<a href="https://colab.research.google.com/github/Ensaf01/Argo_Vision/blob/master/text_hate_speech.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [2]:
import torch
torch.cuda.is_available()


True

In [6]:
!pip install scikit-learn


In [7]:
import pandas as pd
import numpy as np
import torch
from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score, classification_report
from transformers import AutoTokenizer, AutoModelForSequenceClassification


In [8]:
data = {
    "text": [
        "তুমি খুব ভালো মানুষ",
        "তুই একটা গাধা",
        "ওরা সবাই দেশদ্রোহী",
        "এই ভিডিওটা অসাধারণ",
        "তোদের মেরে ফেলা উচিত"
    ],
    "label": [0, 1, 2, 0, 2]
}

df = pd.DataFrame(data)
df


text  label
0   তুমি খুব ভালো মানুষ      0
1         তুই একটা গাধা      1
2    ওরা সবাই দেশদ্রোহী      2
3    এই ভিডিওটা অসাধারণ      0
4  তোদের মেরে ফেলা উচিত      2

In [10]:
train_texts, test_texts, train_labels, test_labels = train_test_split(
    df["text"].tolist(),
    df["label"].tolist(),
    test_size=0.2,
    random_state=42
)


In [11]:
model_name = "bert-base-multilingual-cased"

tokenizer = AutoTokenizer.from_pretrained(model_name)
model = AutoModelForSequenceClassification.from_pretrained(
    model_name,
    num_labels=3
)


/usr/local/lib/python3.12/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


tokenizer_config.json:   0%|          | 0.00/49.0 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/625 [00:00<?, ?B/s]

vocab.txt:   0%|          | 0.00/996k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/1.96M [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/714M [00:00<?, ?B/s]

Some weights of BertForSequenceClassification were not initialized from the model checkpoint at bert-base-multilingual-cased and are newly initialized: ['classifier.bias', 'classifier.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


In [13]:
train_encodings = tokenizer(
    train_texts,
    truncation=True,
    padding=True,
    max_length=128
)

test_encodings = tokenizer(
    test_texts,
    truncation=True,
    padding=True,
    max_length=128
)


In [19]:
from torch.utils.data import Dataset, DataLoader


In [20]:
class BanglaHateDataset(Dataset):
    def __init__(self, encodings, labels):
        self.encodings = encodings
        self.labels = labels

    def __getitem__(self, idx):
        item = {key: torch.tensor(val[idx]) for key, val in self.encodings.items()}
        item["labels"] = torch.tensor(self.labels[idx])
        return item

    def __len__(self):
        return len(self.labels)


In [21]:
train_dataset = BanglaHateDataset(train_encodings, train_labels)
test_dataset = BanglaHateDataset(test_encodings, test_labels)

train_loader = DataLoader(train_dataset, batch_size=2, shuffle=True)
test_loader = DataLoader(test_dataset, batch_size=2)


In [22]:
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
model.to(device)

optimizer = torch.optim.AdamW(model.parameters(), lr=2e-5)


In [23]:
model.train()

for epoch in range(3):
    total_loss = 0

    for batch in train_loader:
        optimizer.zero_grad()

        input_ids = batch["input_ids"].to(device)
        attention_mask = batch["attention_mask"].to(device)
        labels = batch["labels"].to(device)

        outputs = model(
            input_ids=input_ids,
            attention_mask=attention_mask,
            labels=labels
        )

        loss = outputs.loss
        loss.backward()
        optimizer.step()

        total_loss += loss.item()

    print(f"Epoch {epoch+1} Loss: {total_loss}")


Epoch 1 Loss: 1.937369704246521
Epoch 2 Loss: 1.6237932443618774
Epoch 3 Loss: 1.4801400899887085


In [24]:
model.eval()

predictions, true_labels = [], []

with torch.no_grad():
    for batch in test_loader:
        input_ids = batch["input_ids"].to(device)
        attention_mask = batch["attention_mask"].to(device)
        labels = batch["labels"].to(device)

        outputs = model(input_ids, attention_mask=attention_mask)
        logits = outputs.logits

        preds = torch.argmax(logits, dim=1)

        predictions.extend(preds.cpu().numpy())
        true_labels.extend(labels.cpu().numpy())

print("Accuracy:", accuracy_score(true_labels, predictions))
print(classification_report(true_labels, predictions))


Accuracy: 0.0
              precision    recall  f1-score   support

           1       0.00      0.00      0.00       1.0
           2       0.00      0.00      0.00       0.0

    accuracy                           0.00       1.0
   macro avg       0.00      0.00      0.00       1.0
weighted avg       0.00      0.00      0.00       1.0



/usr/local/lib/python3.12/dist-packages/sklearn/metrics/_classification.py:1565: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))
/usr/local/lib/python3.12/dist-packages/sklearn/metrics/_classification.py:1565: UndefinedMetricWarning: Recall is ill-defined and being set to 0.0 in labels with no true samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))
/usr/local/lib/python3.12/dist-packages/sklearn/metrics/_classification.py:1565: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))
/usr/local/lib/python3.12/dist-packages/sklearn/metrics/_

In [47]:
import pandas as pd

texts = [
# Normal (0)
sentence,hate,category
যত্তসব পাপন শালার ফাজলামী!!!!!,1,sports
পাপন শালা রে রিমান্ডে নেওয়া দরকার,1,sports
জিল্লুর রহমান স্যারের ছেলে এতো বড় জারজ হবে এটা একটা দেশের মানুষ কোনো দিন ও ভাবতে পারেনি।ধন্যবাদ তাহসিন ভাই।,1,sports
শালা লুচ্চা দেখতে পাঠার মত দেখা যায়,1,sports
তুই তো শালা গাজা খাইছচ।তুর মার হেডায় খেলবে সাকিব,1,sports
এটা কুন দরনের কেলা ফাইজলামি তাস্কিন রে চর মারা দরকার,1,sports
পাপন ভর মাদা চোদ পাপনে পদতেক চাই,1,sports
দুরো সালার পুদ চুপথাক,1,sports
কুত্তার বাছচা পাপন,1,sports
বাল ছাল তর সাউয়া😡,1,sports
তোর কপালে জুতা মারি শালার পুত,1,sports
পাপনে পাগল হয়াছে,1,sports
দেখেছো মাগি না হিজরা বোঝা যাচ্ছে না। দেখে মনে হচ্ছে হিজরা,1,sports
হালার পু পাপন,1,sports
শালায় এই কারণেই খেলায় ডাব্বা মারে😡😠,1,sports
ব্ব,1,sports
পাপন হালারে বেট থেকে জুতার মালা দিয়এই বের করে না কেনে ওর কারনে ভাল পিলিআর গুলো খেলা পারেনা,1,sports
পাপন মাঘির পুতের পেটের মদ্দে দুর্নিতি ভরা,1,sports
পাপনকে জুতার মালা দেয়া জরুর,1,sports
আমি হলে তো জারসি পড়া লোকটাকে চুদেদিতাম,1,sports
ইয়েছির আলী হালা খেলা জানেনা,1,sports
কুত্তার বাচ্চা পাপন,1,sports
পাপন মাগির পোলার এটা করছে,1,sports
মাগির পুয়া,1,sports
ক্রিকেট মনে হয় ওনার বাবার সম্পত্তি হালার ফু,1,sports
বিসিবির সবকটাই চোরমাদারচোদ,1,sports
কুকুরের চাচ্চা তদেক কি হয়চে নবীকে গারি দিয়াচে তদেক কিচু হয়নি। আর সাদারন একটা মানুষকে গারিদিয়েচে তদেল এত মাতা বেতা বেরে গেছে।,1,sports
মুসফিক চেডের বাল আমার,1,sports
পাপন কে খেলব?কি বলেন আমি কিন্তু হেকার যে ছাইলে পাপনকে মাগির দলাল বানানো কোন বেপারনা,1,sports
সব মানুষ আপন হয় না জেমন পাপন আপন হইতে পারে না শালা হারামির বাচ্চা,1,sports
শালায় আমার একটা পছন্দের প্লেয়ার ছিল কিন্তু রাস্তার কুকুরের চেয়েও খারাপ চরিত্রহীন একটা,1,sports
এগোলি ছাগল,1,sports
তাসকিন কে আমি অনেক পছন্দ করতাম কিন্তু সে যে একটা মাদারি চুদ সেটা আগে জানতাম না। এই তাপ্পর গুলো তাসকিন কে মারার উচিত ছিল??????,1,sports
এ হালার ঘরের হালা,1,sports
এ আগেই তো জানতো তারমানে পিকসিং করছে পাপন মাদার সুদ,1,sports
সব ঠিক আছে হিজড়ার কাছে বাচ্চা চাওয়াটা ঠিক নেই,1,sports
পাপনের পদত্যক চাই শালায় চোর,1,sports
ডিসিপির শালা অন্তরে জুতা মারা উচিত্,1,sports
জারে হালারফুত পাপনতুই বেশি দিন এই জাইগায় তাকতে পারবি নালাখ লাখ মানুষের অভিসাপ দেয়া আছে তর উপর।।সালা ফহিন্নির ফুত।।।,1,sports
দর্শক ছিড়া জুতা মারে নাই তো দর্শক ভালো খারাপ মন্তব্য করতে পারে এতে দোষের কিছু নেই আমার মনে হয় মুশফিক গাঁজা একটু বেশি খায়ছে !!,1,sports
পাপন কুত্তার বাচ্চা এই ভিডিও টা দেখছে কি???,1,sports
সাকিব না খেললে বিসিবির খানকির পোলারা খেলবে,1,sports
পাপ্পুর গালে জুতা মারে তালে তালে।।বেসসার পুলা?,1,sports
বাল জানেন,1,sports
রুবেল ১নং বাইনচোদ,1,sports
পাপন একটা জুয়ারি জদি সাকিব কে ভাত দেয়া হয় তাহলে জিবনে কোনো দিন জদি সুজক পাই পাপনেরে দুই টা জুতার বারি দিমু,1,sports
সালার পুতেরা আর খেলা পাইলো না মারা মারি খেলে।,1,sports
সালা গাজা খুর,1,sports
গাজা খাইচছ মাগির পোলা।,1,sports
চামচাটা নিজেকে নিজে অনেক কিছুই মনে করতেছে।সালা বাবাখুর,1,sports
কুত্তা বাচ্চা এই রকম নিউজ দিস জম্মের থিক নাই।,1,sports
পাপনের মুখটা দেখুন নিজের গদি ধরে কখন জানি টান মারে সেই টেনশন ধরে গেছে শালা গাঁজা খুরি কথা বার্তা তুই আগে পদত্যাগ কর দেখ নতুন কেউ আসলে কি ভাবে চালায়,1,sports
"মাদারচুদ <br />শালা ভিক্ষারীর বাচ্চা<a href=""http://www.youtube.com/results?search_query=%23admin"">#admin</a>",1,sports
পাপনের মেয়ে কে চুদি অনেক বড় মাদাদিচোদ,1,sports
আপনার কথা গুলো ঠিক,1,sports
সব কারশাজি হচ্ছে পাপন মাদারছোদের,1,sports
এই চুদির ভাই তুই কোথায় শুনলি সাকিব ইংল্যান্ডেের হয়ে খেলবে??ক্যাপশনতো দিয়ে বসলি।,1,sports
আমি মুসফিকের গুস্টি চুদি। আমার এখন বাল ফালা,1,sports
খানকির পো তো বাট বাট চোদাস ক্যন বসি বাট বাট করলে তোর পাছায় দিমু পেপে গাচের ডাট,1,sports
কুত্তার বাচ্চারে সরা,1,sports
একেই বলে কুত্তা ভাগ্য কাইশ্যার মতে টা ম্যাচেই সেঞ্চুরি করতে পারল না,1,sports
পাপন সালা পাগল হয়ে গেছে সবাই মিলে একে জুতা মারো,1,sports
বালেৱ সাংবাদিক সাব্বিৱ এৱ শুনামকে ব্যাবহাৱ কৱে অনেমেয়েই লাভবান হতেচায় বর্তমানে সেলেব্ৰেটী ক্ৰিকেটাৱৱাই সবচাইতে বড় ৷মেয়েৱাও জানে ছেলেদেৱ দূর্বলতা কি বাংলাদেশে হাতেগোনা দুএকটা ছাড়া সবক্ৰিকেটাৱৱাই এধৱনে অভিযোগে অভিযুক্ত তাইবলে ব্যাডবয় উপাধি হবেকেন ??? যদি ব্যাডয় হয় সাব্বিৱ তাহলে তাৱসাথে যে মেয়েগুলা মেলামেশা কৱেছে তাৱা ব্যাডগার্ল তাদেৱ নাম কেন আসলোনা ??? অনেক মেয়েৱ ছবি ব্লাৱ কৱা কিন্তু সাব্বিৱে সবি ব্লাৱ কেন হলোনা ? তাহলেকি সমাজে ছেলেদেৱ কোন সম্মানেৱ দামনেই শুধু মহিলাৱ ইজ্জতেৱ দামই বেশী এটাকি বৈষম্য মূলক আচৱন নয় ছেলেদেৱ সাথে এটা হবেকেন যতসব ফালতু চ্যানেল,1,sports
রফিক আমার চেটের বাল🐸মুশি রিয়াদ টাকা দে তাই হেতে ভাব চোদায়🐸,1,sports
এখানে সব কয়টা মারে চুদি,1,sports
সালা মাদার চোত,1,sports
"ছাগলের বাচ্চারা, শিরোনাম কি আর দেখায় কি",1,sports
মুসফিক বাল কামাইছে,1,sports
মুসফিক গরুর মতো চিল্লাইলো 😁,1,sports
ওইদিন রাতে যদি জিল্লুর রহমান কিছু না করে ঘুমিয়ে পড়তো তাহলে জাতিকে আজ এমন একটা কুলাংগার দেখতে হতো না,1,sports
বালের বাল রা গালি দিলে কি এমন বাল হইছে কারে গালি দিছে বাল,1,sports
প্লেয়ারগো পুটকি মার আর এ ই খানকির পুলাগোরেও পুটকি মার,1,sports
তবে <br />তোরা সময় টিভিও <br />মনে রাখ এই সাব্বিরেও এক সময় ভালো সময় আসবে যদিও এখন খারাপ সময় যাচ্ছে ।,1,sports
খেলোয়ার হয়েছে কি বাল ফালানি গেছে,1,sports
তোর মায়ের ভোদা দিয়া কি তুই জন্ম হয়েছোচ না পুটকি দিয়া তোর মা বোনরে কুত্তা দিয়া চোদাই খানকির পুত তুই সব সময় এমন উল্টা পাল্টা জিনিস ছারোছ তো কি জিব্বায় তোর মায়ের মাসিক লাগাইছোচ নাকি কুত্তার চোদায় জন্ম তোর জিব্বা বড় এমন লেহাইয়া লেহাইয়া জিব্বায় বাজাইয়া কথা চোদাছ কেনো,1,sports
তুই হালা,1,sports
এটা আস্থা মিডিয়ার মাগী । ওনি এখন ইসলামের বোরকার নিছে হান্দাইছে । বেহেশতের পুরুষ হুুঁরের অপেক্ষায়। ওনার এখন নাম আমাতুল্লাহ । ওনি বলেছিলেন কখনো বিয়ে করবেন না। শালী এখন হুজুরেরে বিয়ে করেছেন।,1,sports
এই পৃথিবীতে কে এত ভালো মানুষ আছে যারা মধ্যে মেয়ে মানুষের চাওয়া নেই যত সব ফালতু খবর মানুষ জনের খেদে দেএ কাজ নেই মানুষের বেকেতি বেপার নিয়ে এদের মাথা ব্যাথা,1,sports
তুই মাদারচোদ পদত্যাগ করলেই তো হয়। তুই পদত্যাগ করিস না কেন। তুই নিজে তো ধ্বংস করে দিচ্ছিস। একজন জুয়াড়িকে তোর বন্ধু বলতেছিস। গাঞ্জা খায়নি জীবন বলতেছিস। শেষ পর্যন্ত সে জুয়ার সাথে জড়িত জেলহাজতে আছে এখন।,1,sports
এজন্য সাকিবের কোটি পাবে বিজ্ঞাপন করে সেটার জন্য কোটি টাকা লস করবে বাংলাদেশ ক্রিকেট টিম??সাকিবের এতো নিজের সার্থ দেখে কেন?এতো লোভ ভালো না তিন তিন টা খেলায় সে জুয়াড়িদের সাথে কন্ট্রাক্ট রাখছে আই সি সি যে জানায় না কারন কি?জুয়াড়িরা কি সাকিবের দুলা দুলাভাই?,1,sports
ওর ভাবসাব টা কি,1,sports
মাদার চোদরা একটাও ভালো না,1,sports
সালার বোকাচোদার যত সব টাইটেল,1,sports
এ কুত্তার বাচ্চাকে দল থেকে বাদ দেওয়া দরকার।,1,sports
এইসব বালের নিউজ দেন ক্যান। সালারা ভিউ বারানোর জন্য আর কতো মিথ্যা বলবি,1,sports
সালা একটা মাদার চোদ । ঠিক মতো পিটিয়ে হাড্ডিগোস্ত এক করা দরকার।,1,sports
অডমিন সালা এখানে কই বলছে হেপি তুমি কই সালা পাগল ছাগল কই থেকে আসে এগুলা ভিখা কর তাও মিথ্যা কথা কইস না,1,sports
পাপন খানকির পোলাসহমত হইলে লাইক দিন,1,sports
মুশফিক আমাদের বিনোদন দাতা।।।আহামরি কেউ না গালি দিলে ই কি বা না দিলেই কি কামলার বাচ্চা রা,1,sports
পাপন কে বহিষ্কার করা হোক হারামি সালা,1,sports
পাপনকে জুতা এরে ধরে না কে বঝলাম না এটাই কি ক্ষমতার দাপটওকে কে চিনে সালা,1,sports
তুর মাকে কত মানুসকে দিয়ে চুদাভি মাগির পুলা,1,sports
বাকোয়াচ থামনেল চোদাও সালা জোতচোর,1,sports
সালারে হরা আগে,1,sports
মাগি খোর সাব্বির কে বাদ দাও,1,sports
তোর মারে চুদি মাগির পুলা বেশশা মাগির পুলা,1,sports
কেন এই শালা পাপন শভাপতি থেকে সরায়না,1,sports
যে দেশের নাগরিক এখনো খালি পেটে থাকে সেই দেশে এই শালাদের কে কোটি কোটি টাকা বেতন দিয়ে বেপানা করার জন্য সুযোগ দিতেছে হায়রে বাঙালি জাতি কবে তোরা বুঝবি কবে তোরা শিখবি তোদের টাকা দিয়ে তাদেরকে বেতন দেয় কিন্তু তোরা খালি পেটে থাক অশিক্ষিত বাঙালি জাতি,1,sports
মেহেদী হাসান রানা যে বোকাচোদা বোলার তা তম ওভার দেখলেই বোঝাযায়।বার বার ওফ স্টাম্পের বাইরে বল করে ছয় খেয়েছে।,1,sports
পাপন মাদারচোদ 🖕😡😡,1,sports
"রুবেল হেপীরে লাগাইয়া জাইরা দিচোছ,,সালা মরলে বোজবে,?",1,sports
জীবনের প্রথমবার গালি দিচ্ছি ঃকোন কুত্তার বাচ্চা ডিস লাইক দিলি??,1,sports
"বাল শুনেছি তোমার আর -বলতে হবে না,",1,sports
মাগীরা বিয়ে করে পাবে একটা বিয়ে ছাড়া পাবে অনেক নিত্য নতুন এক ঢিলে দু পাখি। বিয়ে ছাড়া যদি আর্থিক আর দৈহিক দুটোই ছাড়ানো যায় তাহলে বিয়ের দরকার কি?,1,sports
বেয়াদব এর বাচ্চা খুব খারপ বেয়াদব সালা বেয়াদব লুইচ্চা 🙄 🐱,1,sports
"রুবেল শালা তুই চিটার,,,,,",1,sports
তর মতো বাইন্চোদরা বাংলাদেশ কে নষ্ট করছে কই বললিনা কখন সে খেলবে ইংলেন্ডের হয়ে,1,sports
বাল ছিল মাদার চুদ,1,sports
বাংলাদেশের ক্রিকেটার খেলা বন্ধ করে দেওয়াই ভালো। যে বালের খেলা খেলে।আবার বয়কট ও করছে!!!! হা হা হা। ভালো খেলে দেশের জন্য কিছু করে দেখাইয়া বেতন বাড়াইয়া চাও।লজ্জা করে না প্লেয়ারদের এসব করতে।আর পাপন সাহেব কেও বিসিবি থেকে বাদ দেওয়া হোক।উনিও ধোয়া তুলসি পাতা না।,1,sports
পাপন সাহেব উপর দিয়ে পানি ঢালে আর নিচ দিয়ে গাছ কাটেসালা একটা আসল মীরজাফর,1,sports
আজাইরা হয়রানি। সবগুলা ছাগল,1,sports
সব শালারা চামচা মুসফিকুর রহিমের। এসব দালালি বাদ দাও কুকুরের বাচ্ছা এসব করে দেশটা নষ্ট করেছো শুধু নেতাদের তৈল মেরে মেরে,1,sports
এই পাপন কুত্তার চাচ্চা গালি দেওয়ার জন্য কেউ মন খারাপ করবেন না।,1,sports
সাকিব না খেল্লে কি হবে হালারপো তোরা আস্তা গাদা।।সাকিব কি হয়ে গেছে এমন ও একটা বেয়াদব।।বাব দেখায়,1,sports
ছোটো লোক যতই ধনী হোউক না কেনো সে যে ছোটো লোক চিরকাল ছোটো লোকই থেকে যায়।,1,sports
বাংলাদেশের খেলা জীবনেও দেখি না হালার বলদ গুলো খেলে,1,sports
পাপন খানকির পোলা এই সব কিছুর জন্য তুই দায়ী,1,sports
খেলায় রাজনৈতি ঢোকে গেছেন শালা মাদার চোদেরা আর কি করবি,1,sports
গালি দিছে তাই কি হইছে বালের খেলোয়ারকে,1,sports
শালারপুত পাপন তোর হাত আছে এখানে,1,sports
মাদারছোধ,1,sports
পাপন সালা তুই আসলেই খারাপ তোর পদত্যাগ চাই তুই সালা সব জানো তুই সালা বড় খারাপ চোর,1,sports
তুমি একটা নডির ছাওয়াল আশরাফুল তোর গুদে বাঁশ দিতে গেছে মাগীর পুর,1,sports
তাসকিন একটা মাদার চোদ্দ,1,sports
ভিডিও না দেখেই তোকে চুদতে আসলাম খানকির বাচ্চা,1,sports
পাপন কুতাবাচা,1,sports
এই শালার মাগীবাজি আর নতুন কি...?? শালারে পাছায় লাথি মাইরা দল থেকে বের করে দেওয়া উচিত। মাগিবাজ পোলাপান দিয়া আর যাই হোক ক্রিকেট হবে না।,1,sports
শয়তানের বাচ্চা রে জুতা দিয়া পিট,1,sports
সাকিব কে যোদি মাসের জন্য নিষিদ্ধ করে। তাহলে পাপনের জাত গুষ্টিরে গরু ছাগল দিয়ে। চোবো।,1,sports
আরে এদের মত পেলেয়ার দের রিজেক্ট দিয়ে দেন। নতুন করে টিম তৈরী করা হোক। শালারা ভাত পাই না চা চোদাই। পাপন ভাই রাইট কথা,1,sports
জার্সি পরা গাঁজাখোর সব ঝামেলা করতেছে শালার টুকাই ভদ্রতা বুঝোস না মানুষের সাথে কিভাবে কথা বলতে হয় গাঁজাখোর জার্সি পরা গাঁজাখোর,1,sports
খানকি মাগীর পোলা সবাই রিপোর্ট মারেন এই মাদার চোদের সব ভূয়া ভিডিও,1,sports
এই সমস্ত মিথ্যাবাদি ইউটিউবারদের জন্য আরমনে চাইনা একটু ইউটিউবে আসি সালা চুদমারানির দলসব,1,sports
এরে পাপন্না সাকিব কে নিয়ে কোনো বাজে কথা বলবেন্নাসাকিব সবার থেকে ভালো খেলেছেসাকিব দুই ইনিংস মিলিয়ে উইকেট নিয়েছেএটা সাকিবের নরমাল খেলাপ্রতিদিনতো সাকিব উইকেট নিবেনা ব্যাটিং এ সাকিব প্রথম ইনিংস এ রান করেছে দুর্ভাগ্যজনক ভাবে আউট হয়েছে য় ইনিংস এ দেখুন রানে অপরাজিতএবং ইনশাল্লা করবেসাকিব আর বাকিরা সব আবাল,1,sports
এই খানকির পোলা রুবেল কই গান গাইছে শুনা মাগির বাচ্চা তর মায়রে তুর বাপের কান্দে ফালাই চুদি ভোদার পোলা....next time no sorry mind it,1,sports
হেতে মাদারচোদ নাচির,1,sports
"শালাই প্রতি রাতে ৭ ইঞ্চি ধন দিয়া মাগি চুদে
",1,sports
উপরের কিছু কিছু কমেন্ট পড়লাম যে গুলো মানুষ নামে কিছু জানোয়ার কমেন্ট করছে কমেন্টএ এডমিন কে তার মা নিয়ে অনেক অশ্লিল গালি-গালাজ করছে যে গুলো কোনো মানুষ করতে পারেনা। আরে জানোয়ারের দল যিনি পোষ্ট করছেন তিনি যদি কিছু দোষ বা ভূল করছে সে করছে এতে তার মা কে অকট্য অশ্লিল ভাষায় গালি-গালাজ করতেছেন কেনো??? আপনারা কি জানেন প্রত্যেক মা- ই পৃথিবীর একেকটা জান্নাত।,1,sports
বাংগালী পাগলের দল,1,sports
রুবেল কে দেখতে চোরের মত লাগে হেপি আপু তুমি কি এর চেয়ে ভালো ছেলে মানুষ পাওয়া নি,1,sports
পাপন কুক্তার বাচ্চা তোর মারে চুদি শোয়ারের বাচ্চা,1,sports
সালা বাট পার চোর,1,sports
পাপন হইলো একটা কুত্তা সুদা,1,sports
গালি আমি দেই ওনেকে দেই তাে কি হইছে বাল ফালাবি গাজাখোর,1,sports
জে এই নিইজ টা ওরে পুটকি মারেন সবাই,1,sports
রুবেল একটা শয়তান,1,sports
সালাকে দেখা জায় কালো কাকে মত,1,sports
এ মাগীর বেটা পাপন শাকিব তো পতাক্ষাণ করছে তোর সম্যসা টা কই,1,sports
এই তোর মারে চোদি,1,sports
মাগির হোলা,1,sports
এই চুতিয়ার বাচ্চাটা উলটা পালটা কথা বলে।,1,sports
ওই হালা তুই এই সংবাদ কোথায় পাইলি?,1,sports
আবাল চুদা টাইটেল🙄🤔,1,sports
পাপনকে পাছায় লাথি মেরে বাহির করে দেওয়া হোকসালা খানকির বাপ,1,sports
নটিরপুএ পাপনের পুটকিমারো তাহলে ভালো হবে মাদারচিদে চাইসে কি সাকিবের সমান হবি তুই তুই তো আমার ভালেরও ষোগ না মাদারচুদ,1,sports
বাইনচোদ,1,sports
পাপন একটা পাগল ছাগল,1,sports
পাপন বলদ তার পদত্যাগ ছাই,1,sports
কুত্তার বাচ্চাদের ভাবা উচিত ছিল আমরা প্রস্তুতি ম্যাচে তাদের সাথে কত বড় ব্যবধানে হারছি তারমানে তারা অনেক ভালো স্পিনার প্লাস তাদের সাথে ঐরকম ফ্রিজে খেলা উচিত যেখানে রান হয় ওইখানে নিজেদের কারণে নিজেরা ভরাডুবি হয়েছে কারো দোষ নাই,1,sports
রুবেল শালা পতিতার বাচ্চা কুত্তার বাচ্চা জানোয়ের বাচ্চা একটা মেয়ের জিবণ নষ্ট করেছিস তর মা বোনের জিবণ অন্ন পুরুষরা নষ্ট করবে শালা পতিতার বাচ্চা,1,sports
জাইল্ল্যা শালারপুত....,1,sports
"মাগির পোলারে দেকতে কেমন লাগে গরু চোর
",1,sports
তর মারে তোর বোন কে তোর চৌদ্দ গোষ্ঠী চুদি হানকির পোলা,1,sports
আর কত জনগনের কষ্টের টাকা নষ্ট করে ওরা।।। খানকিরপোলা বিয়ে করে বৌউ নিয়ে হানিমেন করে ঘরের মধ্য বৌউ ও সাথে ভাল খেলে আর বাংলাদেশ জন্য কি বালের ক্রিকেট খেলে।।,1,sports
হালারপোতোমার জন্য দেশের ক্রিকেট ধ্বংসের পথে,1,sports
পাপন শালা পাসিয়ে দিলু,1,sports
মাদারচোদ তুই পদত্যাগ কর,1,sports
খানকিরপলা পাপন।।।মাদারচদ,1,sports
পাপনের মারে চুদি।,1,sports
আমি ভাবছিলাম একজন ভালো ছেলে কিন্তু না সে একটা চুড়ান্ত বেয়াদব তার উবার লাস্ট বলে যে কাজটা করেছে চুড়ান্ত বেয়াদব ছারা কেহ করতে পারেনা। তার উবারে রান নেওয়াতে যে বেয়াদবিটা করলো মনে হয় সে একজন সেরা বলার। গাদা কুতাকার খেলার মধ্যে হার জিত থাকবেই। যে হার জিত মানতে না পারে তার খেলার কোন দরকার নাই। উবার বল করে দিয়ে বেঁটে নেমে বলে রান করেছে আবার ভাব চুদায় বেয়াদব।,1,sports
দেশবাসি মাননীয় প্রধানমন্ত্রীর কথা অবশ্যই মান্য করেকিন্তু পাপইন্না তুই হালা ছেচকা মাগিরপোলা। তোর টাকলা বন্ধুর লগে তোর পাছায় গাজি পাম্প দিয়া পিডাইতে পিডাইতে চামড়া খুইল্লা মুশিরে গ্লাভস বানায় দিতে মন চাইতাসে,1,sports
শুয়োরের বাচ্চাকে গালি দিলে গালির অসম্মান হয়ওর চেহারা দেখলে আজকাল শুয়োরের ছবি মনে পড়ে।জানোয়ারের বাচ্চাকে সরকার জুতা মারবেনাজুতা মারতে হবে আমাদের মতো পাব্লিকের।,1,sports
বাংলাদের খেলা আর দেখবু না সালা পাপন চুর কয় সে জানেনা কয়দিন আগে সে কইলো ফিকসিনের কতা তাহলে বুজা যায় সব তার সাজানো,1,sports
বলদ কোনুদিন মানোষ হয়না,1,sports
দালাল পাপন শালাএমন ভাবে কথা বলতেছে যেন শে কিছুই জানেনা।,1,sports
আবাল মারকা কমেন্ট বাদ দেন।।পাপন যা করছে ভাল করছে।।আজ ক্রিকেটার রা আমাদের কে কি দিয়েছে?? পারেনা বড একটা কাপ দিতে।। আর ভারতের সাথে গেলেতো বিডাল হয়ে যায়।এক টাকা ও দিয়ার দরকার নায়।পারপমস অনুযায়ী টাকা দিবে।তাহলে ভাল হওয়ার চেস্টা করবে।।সালাদের শরীরে তেল জমছে।।,1,sports
ভোকচোদ সাংবাদিক! পাপনের অপর্কমের কথা বলতেই বোকাচোদা স্যারকে অন্য প্রশ্ন করে।,1,sports
আরে গালি দিয়েছে তা বাল হয়েছে মুশরিফ কি চেটের বাল।,1,sports
রুবেলের চেহারাটা দেখতে একদম কুত্তার মতো।,1,sports
দুই বছর পর কল ট্রাকিং এতদিন কি বাল ছিড়ছে আকসু,1,sports
পাপোন আস্তা মাদারিরছোদ,1,sports
ইন্ডিয়া দালাল হালার পো,1,sports
য়ে চামচা কুত্তার বাচ্চা ধরে রাখছে দেখেই তো মনে হচ্ছে হিরোহিনচি খোর,1,sports
বালের প্লিয়ার গুলা। কিছু পারে না। কর বেশি করে নাচানাচি এটাই পারবি সালা কুত্তার দল।,1,sports
তাছকি আপনি একটা পাগল আপনার বিচার হওয়া দরকার। সবায় পাগল হলেও আপনি পাগল হতে পারেন্না,1,sports
পাপন আর পাপনের মা খেলবে মাচোদা,1,sports
তোর হুগার মোধ্য বাস দিমো,1,sports
বালের কুট কুট মোসাদ্দেক একটারে নিছে সিলেট আর পাইছে না আবার কেপ্টেন অ বানাইসে হায়রে বিনোদন 🤣 এর থেকে আমাদের সিলেট এর লকাল প্লেয়ার তান্না আরও অন্যান্য রা অ অনেক ভালো,1,sports
দূর দূর হালার হালা ই কিজাত গেইম । তাছকিন এতো খারাফ আগে জানতাম না,1,sports
সালা গাজাখুর একটা মেয়ে তার ইজ্জত নিয়া মিথ্যা কথা বলে না ♥♥,1,sports
তুই তোর মার গোয়াদি জন্ম নিচত বাইনচোদ,1,sports
শালা ফালতু।,1,sports
মুশফিক কে গালি দিলে লাগে আর আমার নবীকে গালি কুওার বাচ্চারা তা দেখছ না,1,sports
ইবাদত বেয়াদব ছাগলকে আচ্ছা ধোলাই দিছে সৌম্য 😂,1,sports
পাপন মাদারচুদ পাকিস্তানির সন্তান,1,sports
যে এসব আজে বাজে নিউজ দিতেছে তার গুস্টির মারে ছুদি কিচুদিন আগে বলছে মোসুমী মরে গেছে তারপর বলেছে অারেফিন শুবো মরে গেছে অাজ বলতেছে অাশরাফুল,1,sports
তর মারে চুদার কবর কও,1,sports
তোর মাথা খারাপ না কিরে শালা,1,sports
পাপন একটা কাংকি মাগির,1,sports
সব গুলো জারজ আর পতিতা এর জনম,1,sports
"তুগরে কি পুটকি মারসে শালা
",1,sports
পাপন একটা অনেক বড় আবাল। তাকে বি সি বি তে আর দেখতে চাই না।,1,sports
আচ্ছা পাগল কি বুদ্ধিমান না তুই ছাগলরে বেশি বুদ্ধিমান মনে করস না।গরুর বাচ্চা কোথায় কার।,1,sports
পাপন একটা চুর সালা ওকে বিসিবির সভাপতি থেকে বাদ দেওয়া হোক,1,sports
এই বুইড়া হালার খাটাসের লজ্জা শরম কিচ্ছু নাই। সারা দেশের মানুষ পাপন্নার পদত্যাগ চায় বাট হালায় চরম গুটিবাজ। দেশের ক্রিকেট টাকে ধ্বংসের পাঁয়তারা।,1,sports
সবগুলো ক্রিকেটার জামায়াত শিবির নয়তো জামায়াত শিবিরের থেকে টাকা খেয়ে ধর্মঘট করছে। পাপন হারামজাদার কথা শুনে মনে হচ্ছে একদম দুধে ধোয়া তুলসী পাতা। তুই হারামজাদা ক্রিকেট আর তোর নেত্রী বাংলাদেশটাকে ধ্বংস করার কাজে সদা নিয়োজিত। তবে একটা কথা পরিস্কারপ্লেয়ার যেটা ভালো খেলার পর ট্রিট চায় মুখ ভেঙেতাকে কোন সর্থ ছাড়াই আজীবনের জন্য বহিষ্কার ও দেশ ত্যাগে নিষেধাজ্ঞা এমনকি ঐ দিন পর্যন্ত যত টাকা পয়সা বিসিবি থেকে নিয়েছে সব ফিরত নিয়ে নিবে। কারণ ঐ হারামজাদা খেলেই টাকার জন্যদেশ তার কাছে কিছু না।,1,sports
কানকির পুলাদের জুতা মারা দরকার,1,sports
পাপন হইল এক নম্বর হারামি,1,sports
মুশফিকের ডিসিশান দেখলে মনে হয় গাঞ্জাখাই আবাল মিরাজরে ওপেনিং নামায়।,1,sports
তর মারে চুদি,1,sports
পাপনের গালে জুতা মার তালে তালেপাপন হটাও ক্রিকেট বাচাও,1,sports
আমার মতে পত্যক ক্রিকেটার এখন সাকিবের পাশে থাকা উচিত খেলাটা বন্ধ করে দেওয়া উচিতবলা দরকার সাকিব না থাকলে খেলা হবে নাদেখি বিসিবি কি করতে পারেআবার অনেকে বলবেন এটা কি বিসিবির দোষ নিহে আমি বলব এটা বিসিবির দোসআর সেখানের মুল শয়তান হল পাপন মাগীর পুলায়,1,sports
ভাই পাপনের পদত্যাগ নিয়ে ভিডিও বানান ঐ শালার পদত্যাগ চাই।,1,sports
কিছু ছাগল পাও লাপা লাপি করে নিরিহ দেখে,1,sports
পাপনের পদত্যাগ চাই সালায় দলটাকে আওয়ামী লীগ বানায় ফালাইতাছে,1,sports
চুরের পোলা শালার পুত,1,sports
তুই একটা ছোট লোক তুই কখনই হ্যাপির জন্য ফিট ছিলিনা তুই হলি আন ফিট বয় সেলেব্রেটি লজা করেনা তোর তোকে তো গাঞ্জা খোরের মতো লাগে শালা রংপুরের মফিজ,1,sports
পাপন কুত্তার বাচ্চার পদতেগ চাই পাপন বাংলাদেশের একটি কলঙ্ক,1,sports
মুশফিকের মায়রে চুদি,1,sports
মুসফিক কি বালের খেলুয়ার। অর থেকে ছিনেমার নায়ক রা ভালো আছে।অদের নিয়ে কত বাজে কথা বলে সবাই তার পরেও কোন মাইন করে না।কি মন চলে মুসফিক।ভাব চুদাই।অর ভাবে টাইম আছে। ভুদার পুলা।সামনে পাইলে অকে গুয়া মারতাম।দেখি আমাকে কি করে।ভুদার পুলা।,1,sports
তর মারে তুই চুদ,1,sports
এখানে একটা প্রতিবন্ধী আছে সালা আগে রাস্তা ঘাটে করতো রোস্ট হ‌ওয়ার পর থেকে এখন আর দেখা জায় না 😁😁😁😁😁😁জনি প্রতিবন্ধী,1,sports
সবগুলির জারজ সন্তান এভাবে একটা মানুষকে হয়রানি করার কি দরকার,1,sports
ইন্ডিয়ার কুত্তার বাচ্চারা বাংলাদেশের সাথে এত এত শত্রুতা করে কেন?,1,sports
পাপোনের মেয়ে কে চুদি,1,sports
শালা একটা মাগিবাজ আজীবন নিশিদ্দ করা হক,1,sports
মুশরিকের গেঞ্জি পরা যে লোকটা ওকে দেখলে আমার মনে হয় ও একটা গাঞ্জাখোর শালার পুতে কিভাবে দরছে ওকে আর কিভাবে কথা বলে,1,sports
এটা একটা বালের কাপ শুরু হইছে😡 পাপন গ্রেট মাদারচুদ🖕🖕🖕,1,sports
শালার পুতেরাা মদ খাস আর মাগি চোদোছ না / কয় টা টাকা হইছে তোদের কাছে সুজুন ভাই যে বলছে তোদের কাছে যদি টাকা না থাকে তাহলে এতো বাবু গিরি থাকবে না ।।।,1,sports
ভুয়া নিউস দিস কেন মাদারির বাচা,1,sports
শয়তান পাপ কে সভাপতির পথ থেকে জুতা মেরে তাড়ানো উচিত।,1,sports
শালায়(সাব্বির) পুরাই একটা মাল।😂😂😂😂,1,sports
মনের কথা বললেন,1,sports
মাদার চোদ ভালো খাললে ভালো বলো খারাপ খেললে খারাপ বলো চোদন,1,sports
চোখ দেখছেন?😠😠,1,sports
"তোরা শালারা পতিতার মেয়ে নিয়া টানাটানি করস কেনো,,,,মেয়ে কি আর খুজে পাচ না",1,sports
ইসসস<br /><br />কালাহাসের মুখের ভাষা কি😡মন চায় জুতা মারি,1,sports
পাপন খানকির পোলা এইসব করছে। একটা কুত্তার বাচ্চা। পাপন 🖕🖕🖕🖕🖕🖕 🖕🖕🖕 পাপন🖕🖕🖕,1,sports
মাংগের বাচ্চাদের খায়ে কোন কাজ নাই। সিজারের বাচ্চা । ভক্ত চোদাই,1,sports
তুই গাঁজা খাইয়া আয়ছত সাকিব ইংলেন্ডে হয়ে খেলবে কুওার বাচ্চা ফেমাছ হতো চাছ 🍆🍆🍆🍆🍆🍆🍆🍆এটা তর ফুটকি দিয়া বরমু,1,sports
পাপন চোর হালা,1,sports
পাপুইন্না মাদারচুদ মাগীর ছেলে মাগীর দালান তোরে লাথি মেরে বিসিবি থেকে বাহির করা উচিৎ 😡😡😡😡,1,sports
দালাল মাদারতোষ্ট টা কে জুতা পিটা করা উচিত দশক তো সমালোচনা করবেই মুশফিকের আরো দায়িত্বশীল হওয়া উচিত ছিল,1,sports
এইটা টিক না আমাদের ছোট বেলায় মা ভলতেন গালে পিরিচতা তাসকিন একটা পাগল আর ছাগল,1,sports
সালা লুচ্চা,1,sports
সব কয়টাকে দল থেকে বের করে দিয়ে নতুন দল তৈরি করুক সালা কুওা বাচ্চা রা টাকা জন্য খেলে একটা সিরিজ বাহিরে জিততে পারে না। তাদের কে নোমান দোকান টাকা কয়েন গুলো দিয়ে দে কুওা বাঁ্চা,1,sports
ওদের পাছায় লাথি মেরে বের করে দেওয়া উচিৎফকিন্নি গুলোর তেল জমছে অনেকখেলাতো ভোগে দিছে,1,sports
এই খানকির পোণারা তোদের কি রে গালি ছিছে তাতে তোদের সমস্যা কি,1,sports
তোর মায়রে পাপ তুই যদি ফের এসব থামলাইন ব্যবহার করিস কুত্তার বাচ্চা,1,sports
ঐ কুত্তার বাচ্চা এইটা কি বালের হাইলাইটস হয়ছে?,1,sports
ছাগলল ক্রিকেটার বাদ পড়েছে এখন যতসব ফাজলামি নিয়া পড়ছে,1,sports
পাপন শালা তুই এতো লেকচার না দিয়ে বুকে সাহস থাকলে পদত্যাগ কর!! তোকে বাংলাদেশ ক্রির্কেট পরিচালক হিসাবে চাইনা আর ওরা আন্দোলন শুধু ওঁদের জন্য করে নাই সকল ক্রির্কেটারদের জন্য করছে তুই দেশের ক্রির্কেট এরজন্য কি বাহ কতটা করতেছিস সবাই জানে!! তুই সাকিব মুশফিক মিরাজ এবং সবাইকে নিয়ে বাজে খারাপ কথা বলছিস তোকে জুতা পেটা করা উচিৎ কুকুরের দুই নাম্বার বাচ্চা পাপন মাদারিচোদ তুই তোর নিজের পকেট কতটা বরছিস সেটার হিসাব দে আগে পাপন কাক্কু!! নতুন করে ক্রির্কেট পরিচালক গঠন করা হোক এইটা দেশের ক্রির্কেট বক্তদের দাবী!! চোরের মায়ের বড় গলা যেমন তুই পাপন কাক্কু গলা এখন বড় হয়ে গেছে!! বাহিরে দেশে সব খেলায় লাইভে দেখায় আমাদের দেশে কয়টা খোলা লাইভে দেখাই বাহ দিস সেটা বল পাপন কাক্কু!! এতো খেলোয়াড় দের মধ্যে শুধু একটা মাত্র খেলোয়াড় এর কথা বলি!! ইমরুল কায়েস তোর বউ মেয়ের হোগ্ঙা মারছে নাকি নয়তো ওঁকে দলে চান্স দিস না কেন সেটা বল আগে হারামজাদা কুকুরের দুই নাম্বার বাচ্চা পাপন কাক্কু!! 😡😡😡😡😡😡😡😡😡😡😡😡😡😡😡😡😡😡😡😡😡😡😡😡😡😡😡😡😡😡😡😡😡,1,sports
রুবেল তোর চেহারা যেমন কালো তোর মনটাও তেমন কালো কুকুরের বাচ্চারা তোরা নিজেরা জেনা-ব্যভিচার করছোস কিন্তু আল্লাহকে গালাগালি করস কেন শালা নারী খোর লুচ্চা কোথাকার এদেশের মানুষেরা ইসলামকে ভালোবাসে আল্লাহকে ভালবাসে নবীকে ভালবাসে তোর গালে একদিন জুতাপেটা করা হবে আল্লাহর সাথে তুই কি শব্দ ব্যাবহার করস বেয়াদব,1,sports
কার কি সমসা খয়েছে জার চুল খানি খেয়েছ তাকে কেরাসিন ডালিয়া দাও।,1,sports
তর মা বোনরে চোদি মাঘীর পোয়া,1,sports
সাব্বির বালের খেলোয়ার,1,sports
চুদিরপুত,1,sports
টাকা করার জন্য আর কোন পথ না পেলে তুর মা বোন তো মাগি মানুষকে ভাড়া দিয়ে দিয়ে তুকে জন্ম দিয়েছে । এখন টাকা আয় করার জন্য আর কোন পথ না পেলে তুর মা বোনকে আবার ভাড়া তুই যে ভিডিও করেছস ঐ টা তুর মা বোনকে ঠিক করে দে আমরা ও আসবো তুর মা বোনকে খাইতে,1,sports
লোকমান একটা কুলাঙ্গার,1,sports
শালা পাপন তুই বেশি বারছো 🤬🤬,1,sports
ভূয়া শিরোনাম করলি কেনো সময় টিভির কুত্তারা?,1,sports
তুই একটা মাদারী। তুই কিছু জানছ না।আই সি সি সম্পকর্।,1,sports
"সব দোষ ঐ মাগির, নাম কামায় বড়লোক হতে চেছিলো ঐ মাগি, তুমি পাছা মারা দিতে গেলে কেন? তোমার বাপ কি তোমাকে বিয়ে দিতে পারত না? এখন মারা খাইয়া আল্লাহর দোহাই দিলেই তুমি ফেরেশতা হবে নাকি?",1,sports
বেয়াদব তোর জন্য লায়লা নাঈম বেটার।<br />ক্রিকেট খেলতে দিচ্ছে কে তোকে?,1,sports
চেবলা মাগির পোলা বুয়া খবর দেয়ার জন্য তোর মার বোদা দিয়ে গরম ডিম ঢুকানো হোক 😡😡,1,sports
পাপন হারামজাদা টা কে আবার,1,sports
আমি আল্লার কাছে দোওয়া করি এই এক বছরের মধ্যে যেনো পাপন কুত্তার বাচ্চা কুত্তার মতো মৃত্যু বরন করে,1,sports
ওকে দল থেকে বাদ দেওয়া উচিত।,1,sports
মার শালাকে,1,sports
মুশফিক একটা মাদার চোদ আমার সাতে হলে মুশফিক চাফার দাত ফেলে দিতাম,1,sports
শালা তুই একটা আবাল এসব বাংলা খবর কোথায় পাস,1,sports
ভাই বালছাল দেশে থাইক্কা লাভ নাইবিছিবি সক্ত হইলে সাকিবের মাস সাজা হইতো,1,sports
মামাপাপ বাপরেও ছেড়ে দেয় না সত্য বলার সৎ সাহস দেখানোর পরও আশরাফুলের ক্যারিয়ার নষ্ট করসো রক্ত গরম দেখাইলা। আর মাগিবাজ মালখোররা তুমার বন্ধু ।তর মুখে গু হালার পো হালা।,1,sports
সালারে জুতা পিটা কর পাপোন্দা😡😡,1,sports
বাংলাদেশ পুরো ক্রিকেট টিম মাগীবাজ...,1,sports
জার্সি পড়া এই কুত্তার বাচ্চাটা কে যে এই ছেলেটিকে এভাবে পিছ মোড়া করে ধরে রাখছে জার্সি পরা এই গাঞ্জুইট্টা শুয়োরের বাচ্চাটাকে আচ্ছা মতো ধোলাই দেওয়া দরকার !,1,sports
যেই হারামির বাচ্চা গুলা ডিসলাইক দিয়েছে সেগুলো একটাও মানুষেরচুদা না 😪😪,1,sports
এ গুলা কিয়ামতের আলামত ভাইয়া আর দেরিনাই এই পাপন আমি মনে করি এ সালা একটা চোর সালা বদমাইস জতো সব,1,sports
পাপন একটা বাইচোদ,1,sports
মাতারি শালা,1,sports
শালা রে কাছে পেলে মাইরা ফেলব কুত্তার বাচ্চা,1,sports
সালা তরা পাগল,1,sports
পাপন কুক্তার বাচ্চার মারে চুদি এই মাধারচুদের বাচ্চা পাপনের বহিস্কার চাই,1,sports
খুলনার টিম ম্যানেজন্ট এক নাম্বার পাগল ছারা আর কিছুইনা মেহেদী ছাগলটা একটা মেছ ভালো খেলছে এইজন্য পতিদিন ওপিনিং দেই নামে টা মুখস্ত মারি আউট হয়ে যায় কেন যে এই ভুলটা বার বার করে এখন খুলনার অবস্থা খারাপ,1,sports
"রুবেলের মত কুত্তা কেউ আছে, জাতীয় দল থেকে বাদ দেওয়া হোক।",1,sports
টেকার চোদাদের এমনই হয়,1,sports
এই জন্যই তাসকিন তোরে দলে নেওয়া না তুই একটা পাগল,1,sports
ওই দালাল খাজাখোর টা কে জুতা পেটা করা দরকার ওই কি চেটের বাল।।,1,sports
খানকির পোলারা কিরিকেটাকে ধংশ করিয়া দিতাছে খানকির পোলারা খয়রাতির থেকে কিরিকেট খেলে বরলোক হইছে পিছনের কথা ভুলিয়া গেছে কাপ আনতে পারলে বাংলাদেশে জনগন থাকতে পারতো না,1,sports
খানকির বিয়ে লাগে। নাকি খানকি পুলা না হলে। মজা পাইনা। খানকি কুথাকার,1,sports
অশিক্ষিত ব্যাটম্যান হচ্ছে সৌম্য ছক্কা মারতে গিয়ে ক্যাচ দিয়ে আসে নিজেকে ছক্কার ম্যান মনে করে হালারা কোহলির ব্যাটিং দেখে শিখতে পারে না কিভাবে এক দুই চার ও সময় বুঝে ছক্কা মারতে হয়। আরে নিজের চাহিদা শেষ হলেই তো ছক্কা মারাত যেতে পারতি। রান করার পর মাথা আর কাজ করে না। সারা জীবন তো থেকে গড়ে গিয়ে ধরা খাইছে। সৌম্য ও সাব্বির এর যে প্রতিভা তরা রান না করলেও সমস্য নেই জাতিয় দলের বিতরেই থাকবে সারা জীবন। একটা বড় ইনিংস খেলে নিজেকে এতটা প্রতিভাবান মনে কইর না এটা এমন কিছু না যে চাপা মারলেই,1,sports
তুই হালা চোর তোরে চাটাই করতে হবে,1,sports
পাপন মাদারচোদওর ফাঁসি হয়া দরকার,1,sports
পাপন গালে গালে জুতা মার তালে তালে,1,sports
তামিম বাল খেলছে। শেষ বলে মাছ ধরার কৌশল দেখলাম। কিন্তু ছুটে যাওয়ায় খারাপ লাগল।,1,sports
পাপনের মা রে চুদিবাংলাদেশ বোড মা রে চুদিসবায় বল এক সাথে পাপনের মা রে চুদি,1,sports
মুশফিক কে গালি দিলে কি হবে মুশফিক কি জান্নাতের খুর শালা মুশফিকের গুষ্টি চুদি,1,sports
বাংলার পগল চাগল,1,sports
আবাল হালা বালের পিছ বানায় আবার বড় বড় কথা । কুত্তার বাচ্চারা টা ফাষ্ট বলার এর পিছ বানাইলো না ।,1,sports
এই ভিডিও দেখার পরে আমার মনে হইলো মুশফিক একটা চ্যাটের বাল 😕😤,1,sports
বোকা চোদা চেনেল আবাল,1,sports
লুচ্চা.. মেয়েবাজ একটা..,1,sports
পাপন মাদার চোদ,1,sports
এক বার বলছে নাসির পাপনের মেয়েকে ফুটকি মারছে ।এখন বলবে সাকিব তার বৌর ফুটকি মারছে ।খানকির পোলা কে জুতা মার ।,1,sports
পাপন তুই হলি আসল মাদারচোদতুর সাথে যারা আছে বাংলাদেশ ক্রিকেট বোর্ডে তারা সবাই একেকটা মাদারচোদ,1,sports
সালার পুত মিছা কথা কস কেন?,1,sports
এটা মালাউন,1,sports
"হালা একটা লুচচা,",1,sports
জুতার মুজা দুইয়ে পাপনকে পানি খাওয়াইলে ও টিক হইয়া জাইত,1,sports
শালায় এই কারণেই খেলায় ডাব্বা মারে😡😠,1,sports
দুই বছর অা‌গে পাপ‌নের মে‌য়ে চুদা খাই‌ছে নাসির এর কা‌ছে। তাই ব‌লে বাচ্চা কি হয়‌ছে! হয় নাই।। সা‌কিব অবসর নি‌য়ে নাও।। অ‌নেক হয়‌ছে।।,1,sports
"সাব্বির খেলা পারে না শলা হারামজাদা
",1,sports
এই সব বাহেনচোদদের কারনেই তো ওয়েষ্ট ইন্ডিজের কাছে ৪৩ রানে অল আউট।,1,sports
সিলেট টাকা দিয়ে কি বাল কিনছে সব সবগুলা অচল মাল,1,sports
বাল পাকনা তামার তার।,1,sports
সাব্বির এবার খানিকটা চু*ক,1,sports
জারজ মাদার চোদ,1,sports
পাপন একটা কুত্তার বাচ্চা।,1,sports
মুসফিক কোন চেটের বাল ওরে গালি দিলে কি হবে এই ছেলেদের কারনেই তোরা আজ মুসফিক।,1,sports
আরে আবাল লেখার এস এর এইচ দে বলে তুই শাকিব উচ্চারণ করবি??? উচ্চারণ টা সাকিব হবে। আবাল তুই ওয়ান মিলিওনের যোগ্য না। দোয়া করি তর সাবস্ক্রাইবার যেনো আব্বার ডিক্রিস হয়।,1,sports
মাদারচোত পাপন তুই তো আওয়ামিললীগের কুত্তা না তাই তো,1,sports
মাদার চোদ এই খবর কোথায় পেলি ইংল্যান্ড এর হয়ে খেলবে,1,sports
গালি দেবে না তো কি করবে।তোরা টাকার বিনিময়ে খেলচ। ফাও খেলচ না। লাখ বেতন নিয়া এমন খেললে জুতা দিয়ে পিটানো দরকার।,1,sports
লুইচ্ছা,1,sports
তুর মা ও বোন কে একসাতে সুদতে হবে মাদারিসুদ,1,sports
এই ময়ে একটা মাগি মেয়েরার কারন দেশের এইঅবেছতা এই দরনের মেয়েরার প্রাসি ছাই নাসিরের কুনু দুস নাই সব মেয়ের দুস নাসিরকে দলে ছাই,1,sports
মাদারচুদেরা আফগানদের কাছে হারেওরা নাকি পেলিয়ারসবকটা কে ঘার ধরে বের করে দেয়া হোক,1,sports
নটির পোলা রুবেল তরা আসলে ব্যাশা মাগির পোলারা,1,sports
হ্যাপি তুই ভালো?<br />তুই তো ব্যাশ্যা।<br /> লাগানোর সময় এসব মনে ছিলো না??,1,sports
এই জানোয়ারের মুখ দেখতে গিন করে,1,sports
তুমি তোমার মা এর বোদার টাকা দিসোতুমি যত টাকা ইনকাম করো সব টাকা গুলো তুমি খানকির পোলা তোমার মা এর বোদার ভিতরে সব টাকা সেই খানে বড়ছো,1,sports
সালারা তুরা দেশের টাকা গুলো নষ্ট করতেছে। তোদের খেলার সময় কুটি মানুষ কাজ বাদ দিয়ে খেলা দেখে খেলা না দেখে ঐ সময় টা যদি কাজ করতো তা হলে বাংলাদেশ টা আরো অনেক এগিয়ে যেতো। সরকারের কুটি কুটি টাকা লাভ হতো যদি এই খেলা বন্ধ করে দিতো।,1,sports
খেলোয়ারা হারামি তার পাসে খেলোয়ার নেই,1,sports
মাদারের বাচ্চা বড় লুচ্চা,1,sports
দুরো হালা তাসকিন,1,sports
কালকে চুদিরপো পাপনের বিরুদ্দে ঢাকা মিরপুর স্টেডিয়াম এর সামনে আন্দোলন করবো কে কে আছেন আমার সাথে লাইক দিয়ে সারা দিন যারা সাকিব ভাইকে ভালোবাসেন তারা অবশ্যই আসবেন আমাদের একটাই দাবি চুদিরপো মাদারচোদ পাপনের পদত্যাগ চাই,1,sports
পাপন কুত্তার বাচ্চা হাত আছে,1,sports
জুতা মারো সালারে,1,sports
এই হালারপুতে থাকেই ট্রেন্ড টপিক নিয়া যখন কিছু থাকে তাকেও আর পাওয়া যায় নাসে মাটির নিচে চলে যায়আসল কথা হচ্ছে হালার মাথা ভরা গবর।,1,sports
চামচা গুলা সব মাদারচোদ,1,sports
পুরাই মাদারবোর্ড একটা।। এক ম্যাচে রান পাইয়াই ভাব বাইরা গেসে।। রুশো রে গালিও দিতেসে।।,1,sports
একটা চুতিয়া কাউন্সিল। তারা জুয়ারীদের না ধরে প্লেয়ারদের পেছনে লাগে। হলো ভারতের দালাল। কে বাতিল করে নতুন ক্রিকেট কাউন্সিল করা দরকার।,1,sports
সালার পুত্র মুশফিক কুকুরের বাচ্চা,1,sports
ভোদাই হালা ভালো করে গননা করাও জানে না,1,sports
পাপনের মাকে বউকে মেয়েকে চুদি মাগির পুলা,1,sports
খানকির বাচ্চা তোর মারে চুদি পাফন,1,sports
পাপন মাদারচোদ দেশের ক্রিকেট টাকে ধংস করে দেবে!!!,1,sports
মাগিবাজ,1,sports
"এই সাব্বির, তোকে কি ছোট থাকতে মানুষের পোন্দাইছে ?? তুই তো একটা খাসা মাল তোরে তো পোন্দানো যায়। তোর পুটকিমারতে তো মেয়েদের চেয়ে আরো বেশি মজা লাগবে আমার।",1,sports
ছাগলের বাচ্ছা এখনো পদত্যাগ করিনি,1,sports
খানকির ছুয়াল তর এই চ্যনেল এর গুস্টি চুদা দরকার,1,sports
কয়টা দেশী চুতিয়া মার্কা খেলোয়ারের জন্য কুমিল্লা হারতেছে।,1,sports
গেইল হালায় একটা কূপা,1,sports
পাপন একটা শয়তান,1,sports
শালা বাওন শামিম বোকাচুদা তুই তো সব মজা আরো নষ্ট করে দিলি নরমাল একদম এই আবাল কি আর চেঞ্জ হবেনা😂😂,1,sports
সবই বুজলাম বাইঞ্চোদ রানা আসলো কেন এখানে?,1,sports
আবাল দিয়ে দেশটা ভরে গেছে,1,sports
পাপন কে জুতা মার,1,sports
পাপনা মাগিরপুত নাটক করিস না তোর মা হাসিনা আর তোরা পলানোর পথ পাবি না ইনশাআল্লাহ!!,1,sports
সাব্বির রহমান একটা বালের খেলোয়ার 😏,1,sports
পাপন জারযের বাচ্ছার পদত্যাগ চাই।,1,sports
বাংলাদেশের এক নাম্বার মাদারী এখন,1,sports
লুচ্চামিতে নোবেল দিয়ে দে হালারে,1,sports
মাশরাফির ঢাকারে রীতিমত চুদলো চিটাগাং৷ এখন বুঝ কেমন লাগে,1,sports
শামীম হালার পো 😑,1,sports
সাকিব ভাইকি আর বলবো বাংলাদেশে ভালো কিছুর কদর নাইআর এই খানকির বাচ্চা পাপনযে নাটক করছে সালা তুই কি জানিস নাসাকিব ছাড়া বাংলাদেশ টিম অচলপাপন সালা আবারো ভারতের পা চাটলিসামনে ইন্ডিয়া বাংলাদেশের খেলা ভারত খুব ভালো করেই যানে সাকিব ছাড়া বাংলাদেশ টিম অচল তাই সাকিকে সরানোর জন্য এই প্লানপাপন কাকু তুমি ইন্ডিয়ার নুনু চুসোপারলে সাকিবের টা চুসে দিওকারন তুমিত ইন্ডিয়ার নুনু চুসা লোক,1,sports
খাকির পোলা নান্নু আমার বালের প্রদান নির্বাচ😡সালা আবালের বাচ্চায়😡যেখানে ফিটনেস লেবেলে সবার উপরে ছিলো জহিরুল রাহী কিন্তু তাদের দলে না নিয়া দলে নিছে নান্নুর মেয়র জামাই সৌম্যলিটননাঈমরে😡সালার পুতেরা ক্ষমতার জুরে একেক টা প্রদান নির্বাচকের আসন দখল করে বসে আছোছ😡নির্বাচকের বালের যোগ্যেতাও তদের নাই😡সালারা তদের কারনেই আজ দলের এই অবস্তা আশা করি খুব শিগ্রই বাংলাদেশ দল জিম্বাবুয়ে দলে পরিনিত হবে😡,1,sports
তরা শালা না খেলেই প্লেয়ারদের চাইতে বেশি টাকা মারস তাইলে তাদের ত জলবেই😡,1,sports
বিসিবির এরকম কুলাঙ্গার স্টপ যদি থাকে তাহলে বিসিবিতে এইটাই সম্ভব কারণ দর্শক অনেক কিছুই বলতে পারে মুশফিক আউট হয়েছে দর্শক বলতে পারে ভাই উপরে উপরের দিকে তাকান অন্যায় কি বলেছে বিসিবির,1,sports
হ্যাপি ও রুবেলকে ক্রস ফায়ারে দেয়া হোক। এদের কারনে আজ সোভা নাসিরের মত অনেক নায়ক নায়িকারা তৈরী হচ্ছে। এরা সমাজের কলংখ।। এদেরকে বিদায় দেওয়াটাই উত্তম।,1,sports
রুবেল<br />ছাগল। বাচ্চা রা,1,sports
পাপ নের নানির পুটকি সই,1,sports
এই মাগির পুলা জারজ লীগ মাগি লীগ তাই আর কিছু না পেয়ে কয়দিন আগে পাপনের বউকে চুদে ছিলো তাই পতিশুদ দেয়,1,sports
যারা এই ভিডিওটা ডিস লাইক দিছে তারা মনে হয় খেলার খ ও বোঝে না। সালারা আবাল,1,sports
তোর মরন হ‌ইছে কিনা সেটা বল বাইন চোদ।,1,sports
চামচার বাচ্চারা তোরা সবাই সত্যি কথা বলতেছোর আর এই লকটা মিথ্যা বলছে শালা চোরের ঘরের চোররা,1,sports
খানকির পােলা গানকই,1,sports
"সাব্বির কে রিমান্ড এ নিয়ে গন ধর্ষণ করা উচিত
",1,sports
সাবির very good,1,sports
পপ পোনের গুষ্টি চুদি খানকির পোলা নসুর বাচ্চা,1,sports
পাপনের মাধা চুদে দেও,1,sports
সালা ভিজে বিড়াল।কথায় কথায় ইংরেজী শব্দ ব্যবহার করো। বাংলায় কথা বলসালা এটাকি তোমার বাপের সম্পত্তি পাইছো নাকি।,1,sports
তুর মারে চৌদী,1,sports
মাদার চুদ সব বাঙালী যারে গালি দিছে তার খবর নাই,1,sports
পাপন হালার পুতের পাছায় লাত্থি দিতে চাও কে কে,1,sports
সালা মাদারচোদ,1,sports
পাপন এর মায়রে বউরে মাইয়ারে কুত্তা দিয়া চোদানো উচিত,1,sports
জাতিও পাগল,1,sports
বাংলাদেশ জাতীয় দলের অধপতন পাপন বড় অবদান রাখলহাইরে সালার পুত,1,sports
রুবেল ১নং বাইনচোদ,1,sports
খানকির ছেলে,1,sports
তুমার মারে চুদে,1,sports
"ফালতু কথা না বললে হয় না,খবিস",1,sports
ভারত পাপন হালার পোয়া,1,sports
জারজএরবাচাচাজারজ,1,sports
শালার পুত টাকা না আরো বিষয় আছে,1,sports
তোমার মত বোকাচোদা বোর্ড প্রধান থাকলে দেশের মান এমনিতেই কমে জায়,1,sports
যে আমার কমেন্ট পড়ছো পাপনকে চুদে দাও,1,sports
বালের সাকিব আল হাসান,1,sports
পাপন সালায় একটা বুত্তার বাচ্চা।,1,sports
মাদার চোদ পাপন কে বাদ দেওয়া উচিত,1,sports
খুলনা এই চুতিয়া শান্ত রে দলে রাখে কেন বুঝিনা,1,sports
পাপনের মা বোন রে চুদি বান্দির বাচ্চা ক্রিকেট টারে ধ্বংস করার জন্য উঠে পরে লাগছে বান্দির বাচ্চা মাদারচোদ একটা,1,sports
তুমিকি রাস্তায় কুকুরের মত জন্ম গ্রহণ করেছ?তোমার মা ভালো জানবে,1,sports
শালা মাদারচুদ তাসকিন তোর মা বউ রে চুদি। খানকির বাচ্চা। তোর বউবে কুওা দিয়া চুদাই।তোর সোনা কাটুম যাতে তুই তোর বউরে চুদদো না পারস।,1,sports
গালি দিচে কি হয়চে সালার পিত চামিচ,1,sports
"তুর মাইরে চুদু মাগির বেটা মিথ্যা বলেছুস কেন,,, বেইশ্যা মাগির বেটা",1,sports
ইউ আর বাস্টার্ড বাইনচোদ এসব মিথ্যা খবর প্রচার করার জন্য এই ইউটিউবার হয়েছো তুমি।,1,sports
পাপন হলো বেজন্মা,1,sports
বালের আইন শৃঙ্খলা রক্ষাকারী বাহিনী দেখলো ছেলেটা বিপদে আছে কিছুই করলো না আবার পাবলিক কে বলে দিলো ওইদিকে যাইয়েন না টা ছেলে মন্তব্য করতেই পারে তাই চামচামির বহিঃপ্রকাশ হায়রে পাবলিক,1,sports
শালা ফালতু,1,sports
সব কিছু পাপন মাদারচুদ এর চাল,1,sports
আবাল গুলার বাড়ি নিশ্চই পাবনা,1,sports
তাসকিন কে মরো আগে ছাগল,1,sports
তাসকিন তুই ব্যাটা পুরাই পাগল।এটা কি?????ছি ছি,1,sports
এত বড় একটা বিষয় প্রধানমন্ত্রী কি কোনো ভূমিকাই নিবেন না?মাননীয় প্রধানমন্ত্রীর নিকট অনুরোধ হালারপুত পাপন কে নিষিদ্ধ করা হোক।,1,sports
বাংগালি মুসফিক তুই যে কুওা রাখিস বেসসার চুদা ধোকাবাজ মুসফিক ছেলেটা গালি দেয় নি তার ব্যবহারে পাওয়া যায় আর তোর যে ছাএলীগের মতো কুওা রাখিস বেসসার চুদা ধোকাবাজ বাটপার,1,sports
বালের টিম করছে সিলেটে।,1,sports
হারামী,1,sports
মাদারচোদ আগরওয়ালের হোগায় রড ঢুকানো উচিত।।। 😡😡😡😡😡,1,sports
তরে আমরা আর দেখতে চাই না হালার পুত,1,sports
কুমিল্লার দেশী খেলোয়াড়দের মায়েরে চুদি শালারা টিমটাকে শেষ করে ফেলছে।,1,sports
মাদ্দার চোতকে বাদ দেওয়া হোক সে একটা বেয়াদপ,1,sports
নাজমুল হাসান পাপন আইসিসি থেকে পদত্যাগ করতে হয় এটা আমাদের দাবি এ মাদারচোদ আসল খারাপ ক্রিকেট টিম টাই নষ্ট করে দিবে দেখেন একজন ভালো পিলিয়ার আশরাফুল নাসির হোসেন শাকিব আল হাসান ধ্বংস পাপনের পদত্যাগ চাই সাকিবুল হাসান ফিরে আসুক আমাদের ক্রিকেট,1,sports
পাপন খানকির পোলার পদত্যাগ চাই,1,sports
ডাক দিয়া একপাশে নিয়া জাইতেছে সব সালা রা টাকা খাওয়ার দান্দা এই জার্সি পরা খাজা খোরটা কি এখান কার হায়রে বাংলাদেশ ছি,1,sports
পাপন একটা বুসকি মাগীর পোলা 😠😠,1,sports
খেলোয়ার হইছে মনে হয় বাল ফালাইছে বার বার লজ্জাজনক ভাবে হেরে আসে আবার সাধারন মানুষের উপর রাগ চুদায় খানকির বাচ্চাদের জনগনের টাকায় বেতন দেয়া হয় আবার কিনা সেই জনগণের উপর রাগ দেখায়।,1,sports
খানকির ছেলে তোরমাকে চুূদি গাজা খায়ে ভিডিও বানাও,1,sports
তোরে জোতা মারুম সালা কাসিম টিভি খবর সালা,1,sports
ওই ফোকিরনি তোরে কুত্তার মতো দেখা জায়,1,sports
পাপন শালাই বাইন চুদ,1,sports
পাপন কুত্তার বাচ্ছা। তোর পতন চাই,1,sports
বলদ স্ট্রাইকস এগেইন🤣🤣😂🤣জানে না কোন ক্রিকেটের বালটাও আইছে এখানে কথা বলতে,1,sports
"এই চ্যানেল এর মাইরে চুদি ভুলভাল ভিডিও দেখাস খানকির পোলা
",1,sports
মাদারচোদ পাপন খানকির পোলা এগুলা সব তোর দোষ শুয়োরের বাচ্চা তোর সাজানো খানকির পোলা তোর জন্য আজকে এই শাকিব বাত পরসে আমি তোর পদত্যাগ চাই পাপোন।।,1,sports
পাপনের মায়রে চোদি কি তোর বাপের পদত্যাগ করচ না কেন,1,sports
এই জানোয়ার পাপন সব অঘটন করাইছে টাকা দিয়ে সবাই পাপন কে ঘৃণা কর জুতা মার ও কপালে,1,sports
পাপন তুই একটা মাগির পোলা সালা তুই সব জানিস তুই তো একটা চোর,1,sports
মনে হয় তোকে আর তোর মাকে এক সাথে তাসকিন পেগন্টে করেছিলো মনে হয় মাগী মিথ্যা বাদী,1,sports
শালারা মজা করে,1,sports
বিসিবির মাদারী দুই বছর বাল তুলছে এখন এসে সব৷,1,sports
কিছু কিছু বোকাসোদার কমেন্ট হবে ঠিক এমন👉তাহসিন ভাইর ফ্যান রা লাইক দিয়ে যাও,1,sports
এই সালার পুত,1,sports
বান্দির বাচ্চা সব চামচা,1,sports
কথা দেখে বুঝা যাচ্ছে গালি দেয়নি তারপর ভাব চোদাও খানকির পোলারা,1,sports
সাকিব আল হাসান আন্দোলনের নেতা ছিল সাকিব বিশ্বসেরা অলরাউন্ডার তাকে তো দল থেকে সহজে বাদ দেয়া যাবে নাএখন কিভাবে সাকিব কে বাদ দেওয়া যায় দল থেকেসেই চিন্তা করছে পাপনকোন উপায় না পেয়ে দুই বছর আগের ম্যাচ ফিক্সিংয়ের দায়শাকিবের কাদের চাপিয়ে দিলএইসব নাটক পাপন শালার আমরা সবাই পাপন এর পদত্যাগ চাইওই কুত্তার বাচ্চা বাংলাদেশ ক্রিকেট দলকে ধ্বংস করতে চাচ্ছে,1,sports
এই হারামির বাচ্চা দুই টাকার ক্রিকেটারদের শেখ হাসিনা বেশি আশ্রয় প্রশ্রয় দেওয়ার কারণে আজকে এই অবস্থা হয়েছেদেশের এই টাকা এই সমস্ত ক্লাউন্দের পেছনে খরচ করা উচিত নাএটা একটা অবৈধ প্রধানমন্ত্রী শেখ হাসিনার বাপের একাউন্ট থেকে আসে নাওগুলো জনগণের টাকা।। এত টাকা বেতন দিয়ে এসমস্ত ক্রিকেটার পাওয়ার কোন মানে হয়না।।। টাকা খরচ করে দেশে অনেক ভালো কিছু করার আছে।।।।,1,sports
পাপন শালা পদত্যাগ করছে না কেন???,1,sports
অমানুষের বাচ্চা,1,sports
মুশফিক এর নামে টি সাট পরছে যে লোক টা ওই লোকটা তো গাজাখুর। শালারা তোদের পুটকি দিয়া ডিম দিতে হবে। পাবলিক এর টাকায় খেলে যখন হেরে আসো তখন তোমাদেরকে জুতা পেটা করা দরকার। পাবলিক এখন গালি দিলে গায়ে লাগে কেনো। ডিম মারতে হবে কোন খেলায় হারলে,1,sports
নান্নু শালার পোতেরে সরাইয়া দিলেই সব টিক হবে,1,sports
পাপনরে জুতাপিটা কর সবাই।,1,sports
কাংকির পোলার দরকার নেই,1,sports
ছাগল বড় ছাগল তাসকিন,1,sports
বাংলাদেশের খেলোয়াড়দের দফা দাবি পূরণ করতে হবে আর তা করতে না পারলে বিসিবি সভাপতি নাজমুল হাসান পাপন মাদারিচ্চুদকে পদত্যাগ করতে হবে,1,sports
এই শালা আবালের বাচ্চারা বলতেছে যে গালি দেই নাই তোদের কারণে বাংলাদেশের এই অবস্থা চিলে কান নিল যাচাই করে দেখবেন না,1,sports
রুবেল তোর মুখে জুতা মারি। কুত্তার বাচ্চা তুই নাকি জাতীয় টিমের খেলোয়ার,1,sports
আই কাল্লু রুবেল বল হেপি কি জন্য পাগল হইছিলো....ওয়াক থু রুবেল,1,sports
তামিম ইকবাল কি অাপনার উনার মেয়েকে বিয়ে করছিলো?,1,sports
সব মাদারচোদরাই চামচা।আর জার্সি পরিহিত মাদারচোদটা যেই ভাবে ছেলেটাকে যেভাবে ধরেছে মন চোর ধরেছে।সব মাদারচোদরাই চায়তেছেন ছেলেটার কাছ থেকে ধান্দা করার জন্য উঠে পড়ে লেগেছে ।,1,sports
পাপন নাটক ভালোই করতে পারে শুয়রের বাচ্চা,1,sports
নান্নু একটা মাদারচুদ,1,sports
গালি দিলে কি হইছে বাল ফালানি গেছে মাদার চোদ চামচার দল।,1,sports
মুশফিকের জার্সি পরা বাদাইম্যা চাম চার বাচ্চা বাচ্চা তোরে পাইলে মাগির পোলা পাঙ্গাস মাছের মতো কুচিকুচি করতাম,1,sports
অই সালা চাপাবাজ। কে বিসিবি রে দোষ ছে শালা। দোষ করছে সাকিব শাস্তি ও সাকিবই পাবে,1,sports
পাপন একটা কুক্তার বাচ্চাজানোয়ার,1,sports
সবাইকে একটা একটা চুদা দিন,1,sports
এসব মাগির পোলারা দানদা বাজ চোদানির পোলারা গামজডি মাগির পোলারে আগে মারার উচিত চিল যে বেস্যা মাগির পোলারা চেলেটারে দরছে।ছেলেটার কথা সত্যতা আছে।এ খানকিরপোলারা আজাইরগা মদ খোর পোলারা ছেলেটারে হয়রানি করতেছে,1,sports
বর্তমান সামাজিক যোগাযোগ মাধ্যমে যেভাবে পাপন সাহেবকে গালাগালি করছে ও যদি একবার সামাজিক মাধ্যমের কমেন্ট পড়ে যদি লজ্জা থাকে তা হলেও নিজে বিসিবির সভাপতি তো ছেড়ে দিবে শাকিব আল হাসান হচ্ছে হীরের টুকরো পাপন হচ্ছে ডাস্টবিনের ময়লাপাপনের দুই গালে জুতা মারি তালে তালে,1,sports
হায়রে পাপন মাদার চোদ তুমি জে কি সবাই জানে খানকির পোলা তুই জাইনা সব ঠিক মত সাজায়া এখোন বলস তুই কিছু জানস না তুই মাদার চোদ সব জানস তুই এইগুলা করসস কুত্তার বাচ্চা,1,sports
সব কিছু করছে হারামজাদা পাপন বাইনচোদ ক্রিকেট অর বাব দাদার সম্পত্তি মনে করে,1,sports
খানকি মাগির ছেলেরা মুশফিক তরার মাকে চোদায়। একজন খেলোয়াড় খারাপ ভাল খেলতে পারে। দর্শকেও খারাপ ভাল বলতে পারে। তরা রাস্তার পোলা পান মাদার চোদ তরা কবে যে ভাল হবে। মুশফিক কি তরার মার জামাই। নবীকে নিয়ে কুটর্ত্তিকরে কিছু বলো না প্রতিতালয়ের কনডম ছিরা পুলাপাইন।,1,sports
খানকির পুত পাপন মাদারি খেলবে,1,sports
ভাল করেছে,1,sports
কী অবস্থা গাঁজাখোরটা কী করছে আহারে কী একটা দেশপ্রেমিক পাগল ছাগল।,1,sports
কুত্তালীগের অবৈধ বেশ্যা চরিত্রহীন মাগি পতিতা হাসিনা মাগি সরকারকে সুতার রড দিয়ে চুদানোর কোন বিকল্প নেই।সব মাগি হাসিনার পোষা কুকুর,1,sports
সালা তোর মাকে চুদি খানকির ছেলে,1,sports
পাপন কাজ টা ঠিক করলি না হালারপুত পাপন,1,sports
তুই তোর বাপের পুটকি দিয়ে হইচত,1,sports
কুওার বাচ্চা মাছ দিয়ে শাক ঢাকার চেষ্টা করিস তুই জনগণকে বোকা মনে করিস জনগণ বোকা না তুই পাপন বছর বিসিবির প্রধান থাকবি এমন দিন আসবে সেই দিন তোকে জুতার মালা পরিয়ে রাস্তায় নামিয়ে গুরাবে,1,sports
আমি যতদিন আছি সম্ভব না পাপকে ঘৃণা কর আর পাপনকে নই। বাণীতে মাদারচোদ পাপন,1,sports
বেশি বালফালানি টিম বানালে এই অবস্থায় হবে৷ খানকিরপোলারা সবকিছু কি সাকিব মুশি আর মাহমুদ করবে? আর ফাস্ট বোলার কেন নাই? সাউয়ার টিম বানাইছে মাদারের বাচ্চারা।,1,sports
মিডিয়ার কাউকে কি কেউ বিয়ে করে না? নাকি ওদের বিয়ে হয় না? আসলে তুই একটা লুচ্চা। তাই একটা মেয়ের জীবন নিয়ে খেলা খেললি। তুই চাইলেই মেয়েটাকে বিয়ে করতে পারতি। তোর চেহারা আয়নায় একবার ভাল করে দেখিস। কই তুই আর কই হ্যাপি!!! তুই সুখি হবি ভাবছিস!!!,1,sports
পাপন একটা মাদারচোত,1,sports
এই মাগির বাচচা,1,sports
দাদা নান্নু কুত্তার বাচ্চা কে সরিয়ে দিন!,1,sports
এই সব মাগীগো কোন লজ্জা শরম নাই। এদের ইজ্জতের কোন দাম নাই। এরা শুধুমাত্র নাম প্রচারের জন্য যে কারো সাথে বিছানায় যেতে পারে। এত ঘটনার পরেও মুখ দেখায় কিভাবে? এরা পতিতা।,1,sports
আরে খানকির পোলা পাপন কোটি মানুষ কে কাদিয়ে এভাবে সাকিবের উপরে পোতিসোদ নিলি,1,sports
জার্সি পরা শুয়োরের বাচ্চাটাকে কুওা দিয়ে কামরানো দরকার ছিল মুশফিক কিছু বলে নাই বাকি শুয়োরের দলেরা কি করতেছে দেশটা একমাত্র চামচামির জন্যই রসাতলে গেছে,1,sports
তর মায়রে তুই বাব কুততা কোথায় আশরাফুল মারাগেছে,1,sports
বছর খেইলা বাল ফালায়ছে মুশফিক,1,sports
নান্নু শালারে বাদ দিতে হইব,1,sports
পাপন নডির পুলার কাজ ।সালার পুলা কিছু জানেনা ভাব ল,1,sports
এই সালার বাড়ি কই।বলতে পারবেন কেউ।সালারে জুতা মারা ওচিত।,1,sports
এই আবালচোদা শামিম ছাড়া আর কোনো ভাষ্যকার নেই?,1,sports
সবার আগে এই মাদারটুস্ট পাপনকে বোর্ড থেকে বহিষ্কার করা হোক। একজন আবাল ক্রিকেটের সভাপতি কেমনে হয়?,1,sports
আইসিসি মাদারচোদ,1,sports
চুদির পুলালা ভারতের জিনিস ছারা চলে না,1,sports
এই কাজ গুলা করছে ভারতে সাথে হাত মিলিয়ে পাপন মাদাচুদ,1,sports
সালা real লুচ্চা,1,sports
"এই সালায় কখনও ভালো খেলেনি আর খেলবে ও না,,,অরে না নিয়া ইমরুল কায়েস কে নেয়া উচিৎ ছিল",1,sports
আমাদের জামালপুরের সম্মান শেষ করে দিছে এই সালা,1,sports
তার মারে চুদিয়া হেটার পেলার লয়া আয়চে,1,sports
নুরুরে পিডাইয়া ছাল তুলে ফেলা হোক! ধর্মের নামে ধান্ধাবাজি এই শালারা বেঈমান,1,sports
কুকুরের বাচ্চারা সামান্য বিষয় নিয়ে গেও গেও শুরু করেছে,1,sports
ভাইটাকে দেখে ও তার কথা শুনে বুঝে এবং মুখের অভিব্যক্তি বলে দিচ্ছে তিনি নিষ্পাপ তারপর ও যদি তিনি মুশফিককে খারাপ কিছু বলে থাকে তাহলে বিষয়টা মুশফিক দেখবেন কারণ বিষয়টা মুশফিক এবং ঐ ভাইয়ের একান্ত ব্যক্তিগত। তৃতীয় পক্ষ কেন এখানে নাক গলাতে আসবে এসব নেতা খেতা আমাদের সোনার বালের সঙ্গে বেঁধে বিচি দিয়ে ক্রিকেট খেলা শিখাই😀😃😁😄😂😅 বাংলাদেশ যেহেতু গনতান্ত্রিক দেশ সেহেতু স্বাধীনভাবে মতামত প্রকাশের অধিকার মোটামুটি সব মানুষের আছে। তাদের মধ্যে ও অন্যতম ঐ জামালপুরের ভাইটিও। শুধু মুশফিক না বাংলাদেশের সব ক্রিকেট খেলোয়াড় মাদারচোদের গালাগালি করা উচিৎ এসব খানকি মাগির ছেলেদের খেলাধুলা কোন বালে দেখে আজাইরা বছর ধরে ক্রিকেট খেলে এখন পর্যন্ত আহামরি কোন পারফর্মেন্স নেই। খানকি মাগির ছেলেরা মাগি চোদে কূল পায়না আবার ক্রিকেট খেলবে কীভাবে আফগানিস্তানের সঙ্গে ধবল ধোলাই আবার শ্রীলঙ্কার সাথে ও ধবল ধোলাই খুব লজ্জা লজ্জা লজ্জা এগুলো কোন খেলোয়াড়ের পর্যায়ে পড়ে বেশ্যা মাগির ছেলেরা খেলতে হবে রোহিত কোহলি বাবর স্মিথ হোপ উইলিয়ামসন রুট এবং ফ্যাফের মতো ইত্যাদি ছেলেটাকে দেখতে ভদ্রলোক মনে হয় আর অধিকাংশ বাঙালি দর্শক যে অসভ্য অশিক্ষিত মূর্খ বর্বর ছোটলোক ইতর গরিব এবং বস্তির ছেলে হয়। তা আবার ও প্রমাণ হয়ে গেল। খানকির ছেলেরা ক্রিকেট খেলাধুলার বাল‌ও জানে না আবার আসে আমি বালের ফ্যান তালের ফ্যান সোনার ফ্যান,1,sports
শালারে পাপনরে মার,1,sports
একেবারে সঠিক সিদ্ধান্ত নিয়েছে সাকিবের জন্য আরো একটু বেশি নিষিদ্ধ করলে বেশি ভালো হইতো শালা টাকা টাকা অতিরিক্ত লোভ করা ভালো না,1,sports
গাধা গুলা তাসকিন যে এখনো ছোট বাচ্চা সেইটারই পরিচয় দিল আজ।,1,sports
শালা পাপইন্না গু হারা হারবি,1,sports
বাংলাদেশে জাতীয় দলে জুয়া মদ মাগিবাজি পরিচালনাকারী মধ্যে ভরা।এজন্যই দলের এই পরিনতি। জিম্বাবুয়ে মত দলটা ধংস হয়ে যাবে।বেশির ভাগেই ম্যাচে ফিক্সিং হয়।লাভ হয় জুয়াখোরদের,1,sports
কুত্তা রুবেল তর মুখে জুতা মারা দরকার কুত্তার বাচ্চা একটা মেয়ের সরলতার সোজুক নিয়ে এমন করলি,1,sports
"তদের, মত দুই টাকার মিডিয়ার, মাগির পুতেরা সাব্বির কে নিয়ে সমলচনা করে তদের, মারে চুদি, <br />,সাব্বিরের, বালের সমান, একজন, মানুষ আছেনি এই মাগির, পুতেরা,, শুুধু সাব্বির কে নিয়ে সমলচনা করে তদের কি লাভ,",1,sports
ঐ শালারা এতো কাহিনির দরকার কি ছিলো,1,sports
সালার মাদার চোদ মিথ্যা বলার আর জায়গা পাস না।একটি মেয়ের জিবন নস্ট করে আবার বরো বরো কথা।,1,sports
এই সালা আবুল চোদা কোনটা ঠিক আর কোনটা ঠিক না এটা তরা বুজস না। মাদার চোদেরা মুশফিকুর কি আমার বাল এর মাথা মাদার চোদেরা,1,sports
সালা প্রতিবন্ধী তাসকিন জাতীয় দল থাইকা বাদ পইড়া সালা আবাল জারজ তাসকিন,1,sports
আই সি সি মুখে জুতা মার,1,sports
তৃতীয় দিনে কি খেলা হল মিনিট খেলা দেখার জন্য টিকিক কাটে কেউ বাংলাদেশের সাথে খেলা হলে এটুকুও ভরসা নেই টিকিট কেটে খেলা দেখতে পারব না দিনের লান্জ দূর ডিঙ্ক্রসও হল না খেলা শেষ। কি বালের টিম টো ইনিংশ নিয়ে টা উইকেট নিয়ে ওভার টা ওভারও খেলতে পারল না।।।। বালের টিম,1,sports
চোদনা শামীমের একটা প্রেডিকশন ও খাটে না। বলদের বাচ্চা খেলা তো বুঝেই না উল্টা পাল্টা কথা কয়। মাদারচোদ একটা।,1,sports
নাছির লুচা,1,sports
পাপন নান্নু দুই ছাগল দুইটাকে বাদ দেওয়া হৌক,1,sports
পাপনকে পাগলা কুত্তা দিয়ে খাওয়া করা প্রয়োজন ক্লাবগুলোকে কেসিনো বানানোর মূল হোতা হচ্ছে পাপন তাকে আগের এরেস্ট করার প্রয়োজন ছিল,1,sports
তুই শালা একটা মাদারচোদ,1,sports
পাপন কুত্তুর বাচ্চা মদ খোর এই পাপন কুত্তুরা বাচ্চাকে কি করা যায়টুপি ভাই এই নিয়ে কিছু বলেন,1,sports
শালা ও যদি খেলওয়ার না হতো তাহলে ওকে কে বিয়ে করতো হ্যাপির মতো মেয়ে যে ওর সাথে কথা বলতো এটা ওর কপাল,1,sports
বুকা চুদারে গালি দিছেতে কি হয়েছে সালা আবাল গুলাক দল থেকে বাদ দিয়া দে হালারা একটা জিনিস নিয়ে এতো কিছু করা ঠিক না,1,sports
রুবেলের চেয়ে মেয়ের ও দোষ কম নয়।,1,sports
শালা তুই তো একটা বলদ শুধু বানোয়াট খবর লিখিস,1,sports
পাপন সালার পোলারে পদত্যক চাই কে কে পাপনের পদত্যক চাও,1,sports
সালার বাচ্চা ওই তো খেলা করে বালের মত ওর চে ইয়ে আমার পাড়ার খেলো যার অনেক ভালো খেলে।।।বাল চোদার শুধু নাগিন ড্যান্স এ মানেই,1,sports
মাদার সুদ বালের বি পি এল আয়োজক তার থেকে আমাদের গ্রামের ম্যাচ গুলো আরো ভালো হয়,1,sports
খানকির পোলা তোর লজ্জা লাগে না এসব কথা বলতে? জুয়াড়ির বাচ্চামিথ্যেবাদী পাপন। তুই তো বিদেশে যেয়ে ক্যাসিনোতে জুয়া খেলোস।।,1,sports
আবে চুটিয়া তুই ইসলাম সম্পর্কে কি জানিস? তুই সালাতো ইহুদি,1,sports
সাকিব ভাই ফিরে চায় পাপন কুত্তার পদত্যাগ চায়।,1,sports
চোরের বাচ্চা চোর সালা পাপন ঘোস।,1,sports
সাব্বির একটা বিয়াদব,1,sports
পাপন নান্নু শালা পদত্যগ চাই,1,sports
পাপন খানকির পোলা সব কিছুর জন্য দায়ী তুই,1,sports
পাপনের মেয়ে রে চুদি,1,sports
খানকির পোলা জাড়জ সন্তান মুশফিক আমিও দিলাম কী বাল ফেলাবি ফালা। শালা গাজাখোর এর বাচ্চারা।,1,sports
ইন্ডিয়াকে গালি দিয়া কি করব | আসল কুত্তার বাচ্ছা হইল আমাদের দেশের কুলাঙ্গার সন্তান পাপন | তার কথায় বোঝা যায় পাপনের কারণেই শাকিব সাজা প্রাপ্ত | পাপন শুধু সাকিবকেই সাজা প্রাপ্ত করল নাকি আমাদের দেশের সকল মানুষের সাথে গাদ্দারি করল ??? এটাকি দেশদ্রোহী কাজ করল পাপন ??? বুঝতেছি না!!! নিজে জুয়া খেইলা বেড়ায় বাংলাদেশ ক্রিকেট বোর্ডের টাকা দিয়া আর নির অপরাধ সাকিবকে আর বাংলাদেশের মানুষকে দিল ইন্ডিয়ান বাশ এই বাংলার বাশ দিতি পাপন তারপরও কিছুটা ভাল লাগতো পাপন তুই মানুষের বাচ্চা হইলে নিজে থেকেই নির্বাসনে যা আর কুত্তা চোদার ফসল হইলেই এই দেশেই থাক |,1,sports
হালার পুত পাপন নাছিররে খাইছস এখন সাকিব রে খাইতে চাস,1,sports
রুবেন একটা কুত্তার বাচ্চা।,1,sports
লিটনের নাম কছ নাহ কেন মাগির হোলা,1,sports
খানকির পোলারা মজা করোছনা,1,sports
হালার পুতেরা মাঠে পারে না। ঘরে ভালই পারে।,1,sports
এই সাব্বির ব্যাটা ক্রিকেট খেলতে আসে নাই ও আসছে শুধু লুচ্চামি করতে,1,sports
মুসফিক মাদারছুত কইলাম,1,sports
আবাল চোদা বলে ত মাদারীরচোদ বিশ্বকাপে খেলার চান্স পাই নাই আসলে মাদারীর উচিত ছিলো এটা বা করা থেকে নিষেধ করা কিন্তু হালায় উল্টা লাইভে মারামারির ভিডিও করে দিচ্ছে। কুত্তা ত পড়া লেখা কিছু করে নাই কেমনে কি আর করবো আস্তা একটা বলদ তাসকিন।,1,sports
পাপনরে কোন মাইকে গালি দিলে সুনকে পাব কেউ জানেন শালার পুত রানান আপ এর পুরস্কার নাই কেন।,1,sports
😭😭😭😭 বিশ্বাস করেন অনকে কেঁদে ছি সাকিব ভাইয়ে জন্য😭🙏। সালা পাপন তুই বুঝবি এবার 😡😡😡😡😡,1,sports
পাপনকে জুতা মারা দরকার কুকুরের বাচ্চা আওয়ামী লীগের দালাল দেশপ্রেম নাই পাপনের,1,sports
তামিম জায়গায় দাড়িয়ে খেলতে পারে না বালের খেলোয়ার হইছে।,1,sports
"
কুত্তা পাপন",1,sports
পপক্ ন৷ সালা,1,sports
আর জে সালায় জারছি গায় ওরে পালে আমি ওখানেই ওর চোখ দুইটা উঠায় তাম সালা বাইনচোদ,1,sports
তুর মারে কি চুদছিল নি আশরাফুল।সালার পুত,1,sports
চামচা মায়রে চুদি গালি দিয়েছে তো কি হয়েছে একটু গালি দিয়েছে বলে তোদের গায়ে হাট লাগে আর আমাদের নবীজি কে নিয়ে যে অনেক কিছু বলে ঐ সময় তোরা কোথায় থাকছ দালাল রা,1,sports
পাপন তো জোয়া জীবনে ও খেলে না সে তো কেসেনোতে যায় মোলার জুস আর তেলাপোকা এর সুপ খেতে সালারে ছিরা জুতা দিয়ে মারা দরকার।,1,sports
সালা আবাল,1,sports
সব খানকির পোলা হিরনচি এগুলারে রাখছে কেরা যতসব পাগল ছাগল ছেলেটাকে হুদাহুদি হয়রানি করা হচ্ছে,1,sports
মালুর মায়েরেচোদ্দ,1,sports
আমির সাব্বির কে বলতিছে চুতিয়া বেহেনচোদ,1,sports
এসব আচোদা হুজুরেরা আমাদের ধর্ম ইসলাম কে হাইজ্যাক করছে,1,sports
নবী কে গালি দিলে কিছু বলস না নটির বাচ্চারা আর তাকে গালি দিসে কি হইছে,1,sports
সানিয়া মির্জাকে কি চোদে দিছে সাব্বির!!<br />বালের সাংবাদিক এভাবে শিরোনাম দিছিস ক্যা!! <br />হ্লারপো হালা,1,sports
বাংলাদেশী গুলো চিরকালের কান কাটা কুত্তা। হাজার গালাগালি দিলেও শোধরানোর নয়। এই ধরনের বাংলাদেশী গুলোর জন্যই আমাদের ভারতীয় বাঙালিদের নাম বদনাম হয় 😒 যতসব ছোট লোকের দল।,1,sports
এই পাপন মাদার চোট নান্নু সুজন এই হালারা বাংলাদেশ ক্রিকেট ধংসের জন্য যথেষ্ট । কোন দেশে এই রকম পাওয়ার দেখায় পাপনের মতো । যেন সব খেলোয়াড় রা ওদের গোলাম । মনে রাখতে হবে আমাদের জনগনের টাকায় সরকার সব কিছু চলে । সাকিবের কিছু হলে পাপন মাদার চোট তোর খবর আছে,1,sports
সালারা চোর,1,sports
পাপোন দলের জদি কোনো খতি হয় তাহলে তোরে জবাই করবো কুওার বাচ্চা,1,sports
পাপন মাগির পোলারে আমি পাইলে ওর দুইটা বিচি গেলে দিতাম।😡😡,1,sports
মুশফিক কি বাল বালের প্লেয়ার,1,sports
আশরাফুল গেছে তুর মা ও বোনকে চুদার জন্য কাংকির পুত,1,sports
বেয়াদব লুচচা খানকির পোলা রুবেলা,1,sports
বালের খেলওয়ার।,1,sports
পাপন একটা খানকির ছেলে অর পদত্যাগ চাই চাই চাই,1,sports
কিছু আবাল ইউটিউবে পর্ন দেখতে আসেকিন্তুু সেটা যখন খুঁজে পায়নাতখন তারা বিডিও পাইলেই ডিসলাইক দেও!,1,sports
শালা বালের কিএিকেট খেলে বাদ দেওয়া হওক,1,sports
সৌম্য একটা আবাল চোদা প্লেয়ার ম্যাচ এ টা হাহাহাহা গরুচোদা পারপরম্যান্স,1,sports
শাকিব আই লাভ ইউ আর পাপন কে কে জুতা মারতে চায় লাইক দেন তারা,1,sports
সাবিবর যখন ব্যাটিং এ আসে তখন আমি অনেক থাকি।কিনতু ভাই যখন খারাপ করে তখন জুতা মারতে মন চায়।😄😄,1,sports
সব চামছার দল লোকটাকে যে ধরছে এটা তো গাজাখোর।একটা বলছে তো কি হইছে সালারা দালাল,1,sports
বাইন চুদের বাচ্চা এই গুজব খবর কথায় পাইছে আশরাফুল দুনিয়া ছেরে চলে গেছে এই চারালের বাচ্চার পাছা দিয়ে গরমরড ঢুকিয়ে দিতে হবে।,1,sports
আমি মনে করি সবাই ভালো খেললেও জাকের কিপার কিছু অসাধারণ ক্যাচ আউট করেছে।এজন্য ঢাকার জয়ে বড় অবদান তার অসামান্য বলে মনে করি! এনামুল বালের না পারে ব্যাটিং না পারে কিপিং সালা একটা বোকাচোদা প্লেয়ার।সে নিজেকে হার্ডহিটার হিসেবে যাহির করতে চায় প্রকৃতপক্ষে সে একটা ফাউল আবালমার্কা খেলোয়াড়।তাকে ঢাকা দল থেকে বাদ দেওয়া উচিত।,1,sports
মার জলেনা মাসির জলে কুত্তার দল,1,sports
সালার পুত এইটা তুই কোথায় পাইলি,1,sports
লুচ্চা,1,sports
পাপন মাদারছদ,1,sports
ছি ছি দুইটাই কুত্তার বাচ্ছা,1,sports
পাপোইনা মাদার চুদ,1,sports
পাপোন্দা মাদারি,1,sports
"ফালতু কথা না বললে হয় না,খবিস",1,sports
মাদার চোদ তুই কতা বলিস না,1,sports
ওই তোর মারে চূদি,1,sports
সিলেটের সবডির সুদার মাইঝে দুষ আছে বাইন্চুদ সব😪,1,sports
আবাল চুদা পোলাপাইন😡😡,1,sports
পাপোনেরতো লজ্জা নাই ওকে জুতা মারলে কি হবে,1,sports
যত গুলায় খেলে সব গুলার মারে চুদি খানকির পোলাগো মাদার চুদেরা,1,sports
বোকাচোদা তোমার কথাই তো আমার ভালো লাগতেছে না।ক্রিকেটের জায়গায় তুমি তিস্তার পানি মিশিয়ে দিসো।,1,sports
সবাই বুঝে ভাই । পাপন কুক্তার বাচ্চা জানোয়ারের কাজ। পাপন মাদার চোট,1,sports
সালারে গলায় ধরে বাহির করে দেওয়া হুকওয় ক্রিকেটের কি বুঝেফাউল বাস্টার্ড পাপন,1,sports
দেব চৌধুরী আরেক বাইনচোদ,1,sports
মানু‌ষের মু‌খে আঘাত করা হারাম। হালারা তিনটাই বল‌দের বাচ্চা,1,sports
এই পাপন জানোয়ারের বাচ্চা যত দিন আছেততো দিন আর খেলা দেখবো না,1,sports
এ মাগি তুই বাজারে বাজারে চোদা দে,1,sports
হ্যাপিরে সেই সুদা সুদিছে রে,1,sports
তুই মাদারচোদ এক নাম্বার চোর।খানকির ছেলে তোরাই তো দেশটাকে শশ্মান বানিয়ে দিয়েছিস।পাপন এই অবৈধ ক্যাসিনো থেকে দৈনিক হাজার টাকা পান।,1,sports
পাপনের জুতা দিয়া পিডামো,1,sports
এই মাগির পুতেদের পালে কোন কুকুরের বাচচা।আগে দেশের গুলিকে জুতো দিয়ে পিটালে ভালো হবে বাইনচৌদরা দেশের টাকা নষ্ট করে চোদার খেলা কর? এই দেশের মানুষ এখন ভাত খেতে ভাত পায় না ।,1,sports
তুই তো মাদার চু* ****তর মারে কুকুরে চু***** আন্টির ছেলে।ভিডিও ডিলিট কর।শালা খাটাস সবাই একটা করে রিপোর্ট করুন 🙏🙏🙏🙏,1,sports
আর কাজ পায় না এই পাগল গুলোরে নেটওয়ার্কে দেখাতে হয়,1,sports
কুত্তার বাচ্ছা পাপন তরে সামনে পাইলে জানে মেরে ফেলতাম,1,sports
পাপন একটা খানকির পুলাওরে লেঙটা করে রাস্তায় ছেড়ে দিন!ওরে মাইরা ফেলবে জনতা!বাইঞ্চুদ হইলো একটা মাদারচুদ🤬🤬,1,sports
ভিডিওটার শিরোনাম কোন মাদারচোদে লিখছে? রুবেলকে দিয়াই তোরে চুদানো দরকার।,1,sports
তুমি বাল বুঝ ক কে কলা বানাও তোমাদের মতো রা আগে তোদের কে বেন মারা উচিত,1,sports
পাপনের বাব ভারত আর পাপন শালা একটা চোর গাঁজা খাওয়া বাইনচোদ এর মতো রাজাকার যতো দিন আছে ততো দিন বাংলাদেশের এই অবস্থা থাকবে,1,sports
সালা এই কারোনে বলি কাঙ্গাদেশের মানুষের না শুধু মাটিরও দোষ আছে,1,sports
কনডম দিয়ে চুদবো,1,sports
রু‌বেল খান‌কি মা‌ঘির ছে‌লে‌রে হা‌তি দিয়া পুট‌কি মারা‌তে হ‌বে,1,sports
সব কাজ এই সালা পাপন এর তাকে বিসিবি থেকে বাদ দিয়ে মাসরাফি ভাই কে দেখতে চাই বিসিবি,1,sports
সালা সেই লুচ্চা মুখের ভাষা কি বস্তির ছেলেল চেয়ে নিচের জাতের,1,sports
পাপন হালা সকল নেস্টের মুল,1,sports
"মাদারি সাব্বির
",1,sports
পাপন মাদাচোদের পদত্যাগ চাই বিসিবি থেকে।,1,sports
মাদারচোদ রা লেগেছে ক্রিকেট টা নস্ট করার জন্য,1,sports
অই বাইনচোদের বাচ্চা এই চোদাইন্না ভিডিও আর বানাবিনা।,1,sports
সাকিবকে সবাই মিস করবে । কিন্তু তোদের মত ফালতু ইউটিবারদের সামনে পাইলে বাঁশ দিয়ে দিব হারামির বাচ্ছা । সাকিব পর পর টি ভুল করেছে । বার কি করে ভুল হয় ? সস্তা জনপ্রিয়তা পেতে চাও ??,1,sports
দুজন মিলে তাসকিন বুকা চোদারে মার বানচোদ তাসকিন।,1,sports
পাকিস্তান আসল কথা থেকে?? শালার ধকাবাজ ইউটিউবার,1,sports
পাপন সালার পুত তোর কারণে দেশের কোটি মানুষ কাঁদে,1,sports
পাপন। চোদা,1,sports
কুত্তার বাচ্চারা জনগণের টাকা খেয়ে বেশী বেড়ে গেছে সারা জীবন নিষিদ্ধ করা উচিত,1,sports
তোর মাথা পাগল,1,sports
পাপনের চোদ্দ গুষ্টিকে চোদার দরকার,1,sports
পাপন হালায় পাক্কা অভিনেতা।,1,sports
"এই ছাগলকে কিভাবে পছন্দ করল হেপি!! দেখলেই থু দিতে ইচ্ছে হয়, হারামী রুবেল, ফকিরের বাচ্চা। জেলে পরিবার তোরা সবাই জানা দরকার।",1,sports
আওয়ামী লীগ ক্ষমতায় থাকাকালে সবকিছু হতে পারে খানকির যতদিন বিদায় নামিবে ততদিনে দেশটারে ধ্বংস করে ফেলবে,1,sports
মুসফিক কোন চেটের বাল জে গালিদিলে এমোন হবে জখোন রাসুল কে নিয়ে বাজে কথা বলে তখোন,1,sports
রুবেল<br />তুই জিনিস রে মাদারি😁<br /><br />ছি চুদাইস না😂😂😁<br />হাহাহা😁😁😁,1,sports
সাব্বির এর নাম্বার আছে। সবাই কল দিয়া মাদারিচ্চোদ রে মিসড কল দেন।,1,sports
"বালের নিউজ সম্প্রচার করে সময় টিভি বাল,ক্রিকেটারের বিরুদ্ধে সব আজায় খবর চালায়",1,sports
চুদাচুদি করার সময় কোন মাগি কয়না পরে আইসা মিডিয়া কাছে কয় বুঝিনা বাল কিসে লোভো করে।,1,sports
কুত্তার পেটে ঘিঁ সয় না।,1,sports
"আমি এখনো হতবাক,রুবেল এর মত একটা কুত্তার বাচ্চাকে কেমনে??? জাতীয় দলে রাখা হয়??",1,sports
"সাব্বির বান্ধীর পুত,,,,,,",1,sports
মুশফিকুর রহিমকে নিয়া বাজে কথা বলার অপরাধে এই বাইনচোদকে রাম প্যাদানী দেওয়া হোক।,1,sports
মাদারচান তরে কুত্তার সাথে তুলনা করলাম,1,sports
খানকির পলা সাংবাদিক,1,sports
মাদারচুদ বস্তির পুলা বড় লোক হয়ছে তাই এই অবস্থা।ওর শাস্তি কম হয়ে গেছে।,1,sports
সালা পাপন মানুষ হিসেবে শয়তান ও চোর ধান্দা বাজ,1,sports
হায়রে মুসলমান নবীকে গালি দেয় কোন মাতা ব্যাথা নাই আর ও কি বলছে তা নিয়ে এত মাতা ব্যাথা তাই আমরা গরু খাওয়া মুসলমান,1,sports
তুই মাগির পুলা পাপনকে পাইলে জুতা দিয়ে দেবো মাগির পুলা,1,sports
কুত্তার বাচ্চা পাপন তুই একটা জারজ সন্তানকুত্তার বাচ্চা পাপন খানকির বাচ্চা তোর সময় কমে আসতাছে,1,sports
পাপন হলো মাদারি,1,sports
চোর এর বড় গলা চোর সালা,1,sports
মুশফিকের জার্সি পড়া হালায় প্রফেশনাল গ্যাঞ্জাখোর,1,sports
মাগির পুতেরা গালি দিয়েছে তাতে কি হয়েছে,1,sports
আফগানিস্তান কে যারা ছোট্ট দল বলে অপমান করে বিশ্বকাপ এ আফগানিস্তান কে হারানোর পরে অনেক মজা নিছে তারা কোথায়? মুশফিকুর রহিম মাদারচোদ বেশী লাফাইছে। আজ লজ্জা লাগে না বছর যাবত টেস্ট খেলা দলটা টা টেস্ট খেলা দলের সাথে পারে না। কোথায় মাদারচোদ মুশফিকুর রহিম??!,1,sports
বুঝলাম গালি দিল প্রমান কোথায় সেটার ছেলে টা বার বার বলতাছে গালি দেয় নাই আর মুশফিক আমার কি বালের খেলোয়াড় যে তাকে গালি দেওয়া যাবে না ফালতুর কারনে অনেকগুলো ম্যাচ হারছি,1,sports
পাপন দালালকে জুতা মারা উচিত,1,sports
সালার পুত পাপনরে দেশ থাইকা তারাওর পাছায় আগে ব্লেট দিয়া চিরব তারপর লবন মরিচ দিব😘,1,sports
মাথা উচু করার কথা বলেছে এটাতো আর খারাপ কিছু বলেনি শালা বাইনচুদ বলেতো আর গালি দেয়নী মালিকের চেয়ে কামলারা লাফালাফি বেশি করতাছে যারে বলেছে সেতু মনে হয় ক্ষমা করে দিয়েছে,1,sports
পাপনের পাছায় সিদ্ধ ডিম পুরা হোক।,1,sports
বেশি বড়লোক হতে চায় মাদার চোদগে লাখ তো দূরের কথা চার টাকা ও দেওয়া উচিত নয়,1,sports
"রুবেল তোর বুনকে চুদছে, সালার পুত",1,sports
পাপন কুত্তার বাচ্চা লোকটা ভাল না এ বাংলাদেশের ক্রিকেটকে ধ্বংস আমি প্রধানমন্ত্রীর কাছে একটা অনুরোধ করবে বিসিবি থেকে,1,sports
সালার পোলা,1,sports
ঢাকার মেয়েদের ভুদার ঝালা মিটায় দিছি। কেমন লাগছে ঢাকাইয়া মাগিরা উত্তর দে।লাফা এইবার দুধ গুলা নাচায় নাচাই,1,sports
আলহামদুলিল্লাহ ঠিক হয়েছে শালা কুওালীগ সাকিব,1,sports
মাদারচুদেগোরে ধরে কুত্তার মত পেটানো উচিৎ। মুশফিকরে গালি দিছেতো কি হইছে সে কি আল্লাহর ফেরেশতা নাকি ছেলেটাকে দেখে ভদ্র মনো হচ্ছে গাঁজাখোরের দল তার উপর অন্যায় অত্যাচার করলো আমার মতে এই ছেলেটার কাছে তাদের ক্ষমা চাওয়া উচিৎ।,1,sports
আর ঐ টা কল দেয়া হয় নাই শুধু মাএ এসএম করছিলো সাকিব রিপ্লাই করে নাই আর মাদা চুদ পাপন এখন কথা বলতে আছে কারণ মাদাচুদ পাপন এই কথা বলতে আছে তার গুটি বাজি বন্ধ হয়ে যাবে তাই সাকিব কে নিষিদ্ধ করে দিছি মাদাচুদ পাপন,1,sports
তোরে জুতা মার উচিত বাইনচোদ,1,sports
মাশরাফি তো কিছুই করতে পারেনাই তাই সাব্বিরের উদযাপন সহ্য হয়নাই,1,sports
পাপুইন্যা মাদার চুদ মুলে টিমটা শেষ😥,1,sports
গাজা খুর দালাল খানকীর পুলা চামছা কিছু দালাল ছেলেটা কে শুধু শুধু হয়রানি করলো,1,sports
আশরাফুল শেষঅতঃপর সাকিবও শেষ😪😒😒মাগীর বাচ্চা পাপ্পন,1,sports
মুসফিক কি আমার বাল,1,sports
হালা তোরে সব বলতে হবে।।।।তাইলে তোর কাজ কি।।।তুই আছিস কি জন্য।।।,1,sports
নাটের গুরু পাপন পাগল,1,sports
মাগির পুত পাপন তোর মাইরে চুদি,1,sports
কুততার বাচ্চাদের ভাব দেইখা আর বাচিনা,1,sports
রুবেল একটা গাঞ্জা খোর দেখতে গাঞ্জুট্টি মত লাগে হালা একটা ফকিন্নির পু,1,sports
"তুমি এখন ও বল বয়
",1,sports
দেশের জন্য না খেইলা দেশের কথা চিন্তা না কইরা এখন সব শালারা টাকার পিছনে ছুটা শুরু করছে পাপন বলেন ক্রিকেটার বলেন সবাই।পাশের দেশ ইন্ডিয়া বা অন্য দেশের ক্রিকেট খেলা আর দেশের প্রাতি ভালোবাসা নিয়া খেলা চোখে পড়ার মত,1,sports
লুচ্চার হাফেজ,1,sports
রুবেল ১নং বাইনচোদ,1,sports
গাজা খেয়ে কথা বলিস নাকি সালা এরকম আলটু পালটু বিডিও বানাবি না,1,sports
খানকির পোলা তোর মারে চোদি কৈ রুবেল গান কৌছে,1,sports
পাপন হালার পুত,1,sports
ব্যাডলাগ বলায় কি সমোস্সা খানকির পোলা মুশফিক লাখ টাকা বেতন নাও তোমার মা বোন চোদাইনা টাকা কুত্তার বাচ্চারা হংকং বারমুডার মত দলের সাথেও পারিস না কুত্তার চোদা পাবলিকের টাকা খাও বউ পালো আর একটু খারাপ বল্লেই সাউয়ায় লাগে লাখ টাকা মাদার চোদ ওই চামচা কত্তার বাচ্চা চামচামি বন্দো কর,1,sports
বানদির পুলা তর বৌউ রুবেল নিয়ে গান গাইছে।,1,sports
পাপন কে জুতা মারা উচিৎ,1,sports
পাপইন্না বেস্যা মাগীর পোলার হোগা দিয়া গরম ডিম দেওয়া উচিৎ।,1,sports
ইন্ডিয়ার ঘুস্টি চুদি,1,sports
রুবেলে ছেহারা পাগলে মত বসতি পোলার মত চাগল,1,sports
পাপনকে জুতা নিক্ষেপ করা হোক।,1,sports
হায়রে পাপন তুই আসলে কুত্তার বাচ্ছা,1,sports
শালা মুশফিক কোন চেটের বাল,1,sports
খানকির পুলারা তদের কি খাইয়া কোন কাজ নাই,1,sports
ভাল মুশফিক কে গালি কি বাল হইছে হে কোন হানের প্রেসিডেন্ট আর সব বান্দির পুত দের ভাব দেইখা মনডা কইতাছে ভিডিওর ভিতরে ডুইকা পুটকি মারি সালার পোলারা,1,sports
পাপন কুকুকের বাচ্চা তোকে জোতা পিট করবো তই খরাতি আছিলি আখন তুই আতো বরো কিবাবে হয়েছোথ,1,sports
সব দালাল,1,sports
তোর পুটকি চুদি শালি!,1,sports
খানকির বাচ্চা পাপন তুই কঠিন নাটক বাজতোর বাপে তোর মাকে যে সময় চোদে ঐ সময় তোর বাপ মিথ্যা কথা বলে তোর মাকে চোদছিলআর সেই চুদার ফসল হলি তুই খানকির পোলা পাপন,1,sports
পাপনের ইচ্ছায় যদি সাকিব নিষিদ্ধ হতে পারে?তাহলে কোটি মানুষের কথা পাপকে জুতাপিটা করে আজীবনের জন্য ক্রিকেট বোর্ড থেকে বাহির করা হোক!,1,sports
ছাগলামি ছাড়া নিউজ করা যায় না! আবুল!! 😡,1,sports
ছি ছি ছি। এরা নাকি জাতীয় দলের খেলোয়ার। আমার মনে হয়। এদের জুতো পেটা করতে করতে দল থেকে বাদ দেওয়া উচিৎ। নাতো দলের কলঙ এরা। রুবেলের ধোন গড়া পুছে কেটে দিতে হবে। আর হ্যাপির গুদ বেলাক টেপ মারতে হবে। দুজনার রসটা কম ছিল না। হ্যাপির গুদ কূট কুট করছিল। রুবেল চুদে সাইজ করে দিয়েছে। এখন কাননা কাটি করে লাভ নেই।আবার রুবেলের সাথে দেখা করবি তোর আবার গুল মারবে।একবার শিক্ষা হয়নি আবার চোদা। খাবি বলে লেগেছি? যাইহোক হ্যাপি তোমার মুখে কি দাগ আছে? তুমি শয়তানের রাসতায় থেকে চেহারাটা ইবলীশের মতো হয়ে গেছে। আললার রাসতায় থাকলে চেহারা নুরানী হয়। আপু তোমার নামবারটা দাও অনেক। কথা আছে।,1,sports
কুত্তার বাচ্ছা পাপন,1,sports
ঐ মাদার চুদ কি লেখচিস,1,sports
তোর কি বালের রাগ পাপন😡😡মাদারচুদ😡😡তোকে সাকিবের বাল ফালানোর কাজে দিবো,1,sports
বানদির পুত আর কোন নিউজ পাসনা...? কলকাতার দালাল এই দেশে চাকরি করে এই দেশের বদনাম রিপোর্ট প্রকাশ,1,sports
পাপন মাদারচুদ,1,sports
হাউর পোলা টাইটেল ঠিক কর ভিডিও,1,sports
খানকির পোলারা চামচার দল লোকটা নিদোশ,1,sports
কুয়ার ব্যাঙ সাগরে পড়লে যা হয়।,1,sports
তর৷ মারে৷ তুই৷ চুদ৷ মাগির৷ পোত,1,sports
পাপন শালারে জুতা মারার দরকার,1,sports
শালা মদ খা মানুষ হ অমানুষ এর বাচ্চা,1,sports
"শাব্বির রাহামান খানকির ছেলে
",1,sports
মাঠে তো খেলতে যাও না! মেয়ে দেখতে যাও,1,sports
আমাকে কেউ কারাফ বাবেন না আমি গালি দিমি পাপন কে পাপন তরে আমি জুতা দিয়া বাড়িইয়াইয়া তর মার ফুন্দে দি হারাইতাম কুত্তার বাইচ্চা,1,sports
এই ক্যাসিনোখোরকে আজীবন নিষিদ্ধ করা হোক,1,sports
লাথি মার মাদারচোদ দেরকে।মানুষ খাইতে পারেনা।হেরা লাখ লাখ টাকা দাবি করে।বন্ধ করেন বালের খেলা।যে বাল কাপ জিততেছে ওরা।সাধারণ মানুষের টাকা দিয়া ওদের বেতন চলানো হয় একটা কাপ উপহার দিতে পারে নাই।,1,sports
শামিমের মতো আচোদা কমেন্টারি ছাড়া কি চলেনা?,1,sports
মাগির পুলামাল খাই আবালের মতো ভুল বাল বকিশ,1,sports
শেষ পর্যন্ত সানিয়া মির্জা?,1,sports
কাংকিরপুত পাপইন্নার তর মরে চু,1,sports
তুই মারাজাছ না কেন মাগীর পুলা,1,sports
নাসির একটা কুত্তার বাচ্চা মাদারচোদ শুভ যে কথা বলেছ ঠিক ওর মা ওর একটা জারজ সন্তান না হলে সব ফোন আলাপ করতে পারত না সে,1,sports
আই কুত্তার বাচ্ছা তুই রুবেল বাই নিজে করছে বল্লি কেন,1,sports
ওকে কুত্তা দিয়া চুদানো হোক।,1,sports
কুকরের বাচচা।জুতা দিয়া মারবো।রুবেল বেয়াদব,1,sports
নাটক হণ্ডা শিনে হালার ঘরে হালা,1,sports
এখানে দেখি খানকির পোলারা প্রের্মাস হোয়ার লাইগা এমন কোরে এই লোকটাকে হয়রানি কোরতেছে জার্চি পরা মাগির পুততো হিরনছি খানকির পোলার পোলাটা বার বার কছম বোলতেছে তার পরও হয়রানি কোরলি কেন মাগির পুত তগোরে মুরসিক ভাই কিছু দিবে মনে হয়,1,sports
ডিসলাইক দেওয়া কুত্তার বাচ্চাগুলার ছবি আইডিসহ প্রকাশ চাই,1,sports
আল্লাহ এই পেড মডুর বিচার করুক। সালায় রাস্তায় পইরা মরুক। ক্রিকেট বোড থেকে বাদ হক। সালা আবালের আবাল 💜,1,sports
খানকিরপুলা তোর মাক্কে চুদি। শুয়োরের বাচ্চা তোর মাকে নিয়ে গিয়ে খেলতে বলগা। তোকে কি বুলি গালি দি,1,sports
আরে ওত গালি দিয়েছে তার বাল চিড়িলাও পাগলর বাচচাইন মুশপিকের কাচে তুমাদের বোন বিয়া দিতায়নি,1,sports
শালা মাগির দালাল কুত্তা হারামি হাই ওয়ান,1,sports
পাপোন সহেব আমরা আপনাকে অনেক ভালোবাসি আপনে সকিব আলহাসান ভাই কে দলে ফিরিয়ে ন্যন তানা হোলে দেশের হোগামারা যাবে,1,sports
এত চুদাচুদির খায়েস।। শালা মাগা মাগি দুইটা,1,sports
ফকিন্নির বাচ্চাদেরএত টাকা থাকতেও মন ভরে না। কি ফ্যাশন এক একটা খেলোয়াড়দের ও তাদের পরিবার এর।।।আরও টাকা দাওআর দেশের কোন উন্নতির দরকার নেই।। মাশরাফি বাদেসবগুলা নিজেদের ঝুলা ভারি করা নিয়ে ব্যাস্ত।।।,1,sports
সম্মানের খাতিরে কিছু বললাম না ভারত সিরিজ যদি হয় আর বাংলাদেশের অবস্থা যদি খারাপ হয় তাহলে সাকিবতামিমমুশফিকের কি অবস্থা হবে! জুতা নিয়া রেডি থাকবে সবাই বিমানবন্দরে,1,sports
দুর সালা বাইঞ্চুদ ইউটিউবার,1,sports
আমাদের দর্শক মাদারচুত কম না,1,sports
ওর জন্ম বস্তিতে হইছে আমি সিউর। 6 মাসে কি বাল হবে???? আজীবন করলেও কোন যায় আসেনা। আমাদের দেশে প্রতিভার অভাব নাই।,1,sports
শালার পো পাপন তুই একটা মাল,1,sports
ছেলে মানুষ ইনজয় করবেই,1,sports
ওর মা আর বোনরে সবাই গনহারে চোদেন,1,sports
সাব্বিরে মারে চূদি,1,sports
পাপন হালায় মাদারি,1,sports
পাপন সালা একটা দুর্নিতির গুডাউন। দেশের সরকার তাকে সাহাজ্য করে,1,sports
আর সৌম্য চুদিরভাই এইডা একটা শট খেল্লি জাতীয় টিমের ওপেনার হয়ে আর কবে খেলা শিখবি😡😡😡,1,sports
না জেনেই আবালের মতো কথা বলা উচিৎ না,1,sports
ক্রিকেটারদের আগে জনগনের কাছে চলে আসছে তুমি শালাবাবু চোর। তুমি এবং তোমার ছেলা পেলার পদত্যাগই বিসিবির উন্নতি। বাংলাদেশ ক্রিকেটের উন্নতি।,1,sports
তারজনও কাদতে হল তাসকীনের শালা পাগল,1,sports
"সাব্বির বালের খেলোয়াড় কোনো কামের না,",1,sports
কে কে পাপনের মায়রে চোদতে চাও তাহলে লাইক দাও,1,sports
মুসপিকের মায়রে আমি চুদি হেডাম থাকলে কিছু করি দেখা,1,sports
পাপন হালায় নিজেই বড় একটা জুয়ারু,1,sports
পাপন ভাজা হচ্ছে মাদারচোদ দুই নম্বর মাদারচোদ নাননু,1,sports
দর্শকের সাথে যারা খারাপ আচরন করছে সব কয়টা কুকুরের বাচ্চা আর রবি নামের কুকুরের বাচ্চা গাঁজা খোর ইয়াবা খোর ফেনসিডিল খোর অনেক খারাপ আচরন করছে গাঁজা খোর কিভাবে গ্যালারিতে আসে দর্শক ভালো খারাপ মন্তব্য করতে পারে এতে দোষের কিছু নেই !!!,1,sports
পাপোন হারাম জাদা,1,sports
কুত্তার বচ্ছা পাপোন কে গুনো পিটোনি দেওয়া দরকার,1,sports
কুততার বাচ্চা পাপনের পদতক চাই,1,sports
মুশফিক আমার বাল সালার মাদার চোদ মুশফিক,1,sports
হালার পুত পাপন😠😠হ্লা নমরুত ফেরাউন ও এত্তো বড দোখাবাজ ছিলনা!!হঠাও পাপন বাছাও ক্রিকেট✋✋,1,sports
"যে চোদা খাওয়ার সে ত চোদা খাইবেই<br />,,রুবেল ভাই,আমি তোমাকে সাপোর্ট করি,<br />মেয়েরা যখনন রাস্তায় রঙ ঢং কইরা বেড়ায়,,তখনেই ত মনে কয়,, শালিরে এখনি ফেলাইয়া চুদি",1,sports
বাইঞ্চোদ পাপইন্না চুদানির পুলা,1,sports
মাগির বাচ্চায় অ মানুষ ভাই পাপনের পতন চাই,1,sports
এখান থেকে শিক্ষা নেওয়া উচিত বাংলাদেশ গভারমেন্ট কেননা বঙ্গবন্ধু বিপিএল দেওয়াতে বর্তমানে কোন পাবলিক ক্রিকেট দেখতে আসে না এখনো সময় আছে মানুষের কাছে গিয়ে অতি বিলম্বে কমা চান কুত্তার বাচ্চা পাপন,1,sports
খানকির পোলা তুই সত্যি জানস না,1,sports
এই খানকির পোলা পাপন তুই বের হো বিসিবি থেকে,1,sports
আপনি যখন পরিচালক ছিলেন তখন কোন বাল ফালাইছেন।,1,sports
জারছি ওলা মাদারচুদ মুসফিক কি তর বাপ লাগে। সত্ত মিথ্যা না জেনে চাইমচামি করিস না। মুস্ফিক তর কান ওয়াস কারাইস বিসিবির ভিতরে পুলিশ ছাড়া কুনু চামচার আইন চলবেনা। খেলুয়ার দের টাকা সরকার কার কাছ থেকে দেয়। চামচার বাচ্চারা। মুস্ফিক ভদ্র পুলা হইলে দরসক ভুল করছে ও বুঝাইতে পারতো। সালারা গরম দেখাও। নবিজিরে গালি দিলে গরম দেখাইতে পারনা। বাঞ্চুদেরা। সরকার কুটি কুটি টাকা দেয় তদের ভালো করে খেলতে পারছ না। ভাব দেখাও,1,sports
এটা রুবেল এর কন্ঠ না ছাগলের বাচ্চা রা,1,sports
পাপুইন্না মাগির পুত রে দেখলে মনে করে লাতি মারতাম,1,sports
পাপনকে উচিৎ জুতা পেটা করা ।,1,sports
এ খানকির পুলা গান কই,1,sports
"শালা বাংলাদেশি মাদারচুদ
",1,sports
কুত্তার বাচ্চা মিথ্যা হেডলাইন দেছ কেন,1,sports
বাংলাদেশের যত টুর্নামেন্ট হবে কেউ বাংলাদেশের খেলা দেখবেন নাবাংলাদেশ এখন মাদারচোদ দেশ টয়লেটে করতে গেলেও রাজনীতির পাল্লায় পরতে হয় রিক্সা এক্সিডেন্ট করেছিরাজনীতিতে এসেছে বিমান এক্সিডেন্ট হয়ে সব মারা গেছে 😁😂,1,sports
গান্জাট্টি সালা এত পাওয়ার পাই কই সে একটা ভুল করে থাকলে তারে পুলিশ প্রশ্ন করবে!,1,sports
খানকীর পোলা মুশফিক,1,sports
কি খেলে শালারা,1,sports
কালা পাঠা তুই একটা মেয়েৱ জীবন নিয়ে খেলাটা ঠিক হয় নাই,1,sports
শালারা সব চামচা,1,sports
সব মাগীর পোলারা মুশরিকের চামচা,1,sports
মাগীর রাজা - মাগরাজ 😉,1,sports
শালা গর কোন কাজ নাই,1,sports
সালারা সব চুর।পাপন হালা।কত দিন,1,sports
তর বাপের কিরে খানকির পোলা।,1,sports
খানকির পোলারা খেলা পারেনা আবার ফুটানি চোদায়!! বকা দিছে ভালো করছে। মুশফিক কি তোগো বাপ লাগে মাদারচোদ!! শাকিবার পাল্লায় পইরা সবগুলা খেলোয়ার বস্তি হইয়া গেছে।,1,sports
সবকটা মাদারচোদ খানকির পোলা ভাইয়াটা বুঝাইতে চাইছি কি আপনি জানেন এই ভাইটি বুঝাইতে চাইছেন মুশফিক বাইরে গুডলাক আবার হবে মানে আপনি আউট হয়েছেন মন খারাপ তো দরকার নাই নিচে তাকানোর দরকার নেই উপরে তাকান আবার হবে,1,sports
এই মাদাচুদের বাচ্চারা তোদের মা বোনকে গালি দিলেত কিছু বলতে পারিস না খানকির পুলারা মোশফিককে কে কি বলছে তার জন্য লোকটাকে ধরলি মোশফিক কি তোদের বাপ হয়,1,sports
কোন কুত্তার বাচ্চায় ভিডিওটা ছাড়ছে????,1,sports
সালা বাটপার তুই,1,sports
খানিক পুলা মাদার চুদ পাপন,1,sports
গালি দিছে কি বাল হছেনি খারাপ খেলবে সারা দিন আবার কিচু বলা জাবেনা পাবলিকে টাকা গুলাম তারা খারাপ খেলে পাবলিক অনেক কথা বলবে মেনে নিতে হবে।।।। আর তোদের নবিকে গালি দেয় তোদের কনো কথা নাই আর মুসপিকে গালি দিছে এটা কি না করতে ছে,1,sports
টুকায় মনে হয় রুবেলকে,1,sports
তুমি চুদির ভাইপদত্যাগ করা তাহলেই সব ঠিক হয়ে যাবে,1,sports
এই ফহনি পোলাও হলো মাদার চোদ,1,sports
ছাব্বির ছাগলের ভাব দেখলে বাচিনা তাকে কুমিল্লার দলে নিয়ে দল টা কে পুরা অসম্মান করে দিলো তাকে জাতীয় দল থেকে বাদ দেওয়ার দরকার,1,sports
কিরে তুই সাকিবকে পুজি করে পাপনকে জুতা দেখালি সেই জুতা তকে দেয়ার দরকার তুই মানুষকে ভুল দিকে টেলে দিয়েচিস আজে বাজে ভিডিও বন্দ,1,sports
কুত্তার বাচ্চারা জনগনের টাকাই ফুর্তি করবেদেশের ভাবমূর্তি নষ্ট করবে। রাস্তায় পেলে আচ্ছা করে পিটানো দরকারভবিষ্যতে যাতে এমন কাজ করতে সাহস না পায়,1,sports
হাই বন্ধু রা আমার নাবার আমি সেক্স করি আমার নাবার,1,sports
পাপনের মায় রে চুদে দে মাগির পোলা তোর কপালে দুংখ আছে,1,sports
গাদার বাচ্চা মুশফিকের পিছনে তোর বাপ,1,sports
পাপন জুতার পিটুনি খাবে সেই দিন আর দূরে নাই,1,sports
পাপনের পাছায় লাথি দিয়ে বোর্ড থেকে বাহির করে দেয়া দরকার এখনি,1,sports
তোর মা চুদি,1,sports
মুসফিক কি যে একদম ভাব।কি বাল,1,sports
আমি গালি দিতে আছি মুসপিক মাদার চোদ আমার বাল পালা,1,sports
এসব মাগিদের কে কেন এগুলা দেওয়া হয় এগুলোকে ফাঁসি দেওয়া উচিত তবে তার তার তাড়াতাড়ি জেনে নেওয়া হোক এসব মেয়েদের জন্য অনেক ছেলেদের নষ্ট জীবন,1,sports
মুশফিকের খেলা কে অনেক পছন্দ করতাম কিন্তু ও যে মাদারচোদ এটা জানতাম না এই ছেলেটা কি এমন অপরাধ করেছে মুশফিকদের একটা বেয়াদব এটার পরিচিত সে নিজেই দিল তোদের মতন টিকিটের ড্র সাপোর্ট না করতাম ভিক্ষা কইরা ভাত পাচ্ছিনা,1,sports
খানকির পোলারা একটা খেলা জিততে পারে না । জনগনের টাকায় বিদেশ ঘুরোস গাড়ি বাড়ি কিনোস । জার্সি খানকির পোলারে খুব শিগগিরই রাস্তায় পাঠানো হবে । কেন্টিনে কাজ করে হলায় ।,1,sports
যারা ডিজলাইক দিয়েছে তারা কুকুর চোদা,1,sports
সালারা গাজা খাইছে তা না হলে লোক টা কে কথা বলতে দেয় নাই,1,sports
ইন্ডিয়া খানকি মাগি হগোল বাংলাদেশ কে খেয়ে দিছে,1,sports
মনডা চায়তাছে হালাগোর খেলায় আর দেখোম না গাঁজা খোর এর বাচ্চা,1,sports
লুচ্চা সাব্বির ...,1,sports
শালার একটা ......Mc,1,sports
শালা পবন ভারতের দালাল টাকা নিয়েছে ভারতের কাছ থেকে,1,sports
তর চৌদ্দ গুষ্টিরে পুটকি মারছে নি আশরাফুলে,1,sports
রুবেল আর বস্তির পোলা নাসির এই দুই সালা বাংলাদেশ ক্রিকেটের মান সম্মান নষট করছে সালা সাওয়ার পোলাপান,1,sports
এটা হচ্ছে ইউটিউব থেকে টাকা কামানোর দান্ধা তর সালা বাইন চোদ,1,sports
দালাল শালা,1,sports
প্রত্যয় হীরণ হতে চেয়েছো বেটা নাহিদ? বোকাচোদা নাহিদ এতবড় আল্লাম্মা এরা এমনি হয়নি।ওদের ভুল না ধরে নিজের আখের গুছা। পরের ভুল না ধরে ভালো ভিডিও বানা শয়তান। তোরে কয়জনে চিনে?ওদেরকে হাজারহাজার মানুষ চিনে। অযথা নিজের কুচরিত্রমার্কা ভুল ধরার গান্দেগী ওদের উপর না দিয়ে বিশৃংখলা না করে শান্তির ভিডিও বানা। নয়তো দুচে দিনো তোর চৌদ্দগুষ্টিকে কথা কি ক্লিয়ার না ভেজাল আছে শয়তানের দোসর👹,1,sports
"সালার পুলায় বালের খেলোয়াড়
",1,sports
আমরা সাকিব ভাইর পাশে আছি৷ এবং পাপনকে জুতার বারি দেও,1,sports
এই সময়ে সাকিবকে ব্যান করাটা ইন্ডিয়ার চক্রান্ত! বাংলার ক্রিকেটের মাথাটা কেটে আলাদা করে ফেলেছেএই পাপন মাদারটোস্ট🤬,1,sports
সবাই আন্দোলন করে পাপনকে স্থায়ী ভাবে বহিস্কার করোন। আর না হয় গণপাবলিক ইট পাথর ছুটিয়ে মেরে দেন সালারে,1,sports
প্রতিবাদি সাকিবকে কি ভাবে রুখে দিল বিসিবির পাপন সালা,1,sports
ওই খানকির পোলা হিরো দালাল দালাল ওই খানকির পোলা বাবা খায় চেহারা দেখে বুঝেন না যে পূরণের দরসি পড়লে বর্ধমান দেখতে তো বুঝা যায় মার জলেনা মারানির জলে,1,sports
কিছু কিছু আবাল কমেন্ট করছে পাপন পদত্যাগ করবে পাপন আসার পরে ক্রীকেটের অনেক উন্নতি হইছে।তোরা কি চাস তোদের বাপকে বসাবী বোর্ডে।,1,sports
কোন মাগির ছেলের জন্য সকলেই নিষেধাক্কা দুর্ঘটনা এখনকার মাধ্যমে প্রকাশ হলো সেটাই জানেন না এই ঘটনা আমাদের বাংলাদেশ অনেক বড় ক্ষতি হবে না থাকাতে,1,sports
এই সালা <br /> জুতা মারো,1,sports
মজা না পাগলে পাগলামী করতেছে।,1,sports
সাকিব ভাই আমরা আছি তুমার পাশে তুমাকে অনেক মিস করবো ভাই পাপন শালার পুতকে যদি সামনে পাইতাম। তাকে জুতা দিয়ে মারতাম বাংলাদেশ টিমটাকে সে ধংসের দিকে ঠেলে দিছে,1,sports
নান্নু পাপন কুততার বাচ্চা আমি ভারত ইন্ডিয়ান থেকে পদত্যাগ চাই এই কুর্তা দের,1,sports
তুরা নাব্বার ছারা পাগল,1,sports
বলদের দল,1,sports
পাপন আমার মন চাইতেছে তোর গালে জুতা মারতে তুই এক বাপের চোদা হয়ে থাকোস তবে পদত্যাগ করবি,1,sports
ভুয়া খবর দিলে চুদা খাবি শ্লা,1,sports
শালা একটা লুচ্চা,1,sports
তুই ডাডি মা রে ছুদি,1,sports
পাপন শালার লজ্জা নাই। খেলোয়ার চাই না পাপন আর থাকুকতর যদি সরম ন থাকে তাহলেতুই পদত্যাগ কর ভাইশালা ঘুষ খাইতে খাইতে চিবহা বড় হয়ে গেছে।,1,sports
বরিশাইল্লা টা কি করে হালা আসল খোর,1,sports
জুতা পেটা করা উচিত মুশফিক কে,1,sports
তোরে জুতা মারার দরকার,1,sports
শালার পাপন রচনা পাঠ করতেছে,1,sports
তুই সালা তাড়াতাড়ি মরবি তুই যে কথা বলছোছ তর মা-বাবা মরার কথা বলতে তর মুখে একটু বাচবো না! সালা ব্যানচোদ,1,sports
পাপন খানকির পোলা আল্লাহ তোর বিচার করবে 😭😭😭😭😭,1,sports
কানকির পূ,1,sports
মাগীবাজ হালারে আজীবন নিষিদ্ধ করা হোক জাতীয় দল থেকে।আশরাফুল ভাইকে খেলার সুযোগ করে দেওয়া হোক।,1,sports
শালা খারাপ,1,sports
ভিডিওর সাথে কথার মিল নেই কেন ওই কুত্তা,1,sports
সালারপুতেরে জুরে একটা থাপ্পড় মারতে পারতাম😠😠😠😠,1,sports
এই জন্যই শালারা বিয়ের পর খেলতে গিয়ে চেঞ্জ ঠিক থাকেনা এই মাল পাইয়া খেলায় মন বসে না,1,sports
সালা মালুর বাচ্চাদের কি বলি ভাষাই খুঁজি পাচ্ছি না।,1,sports
ভাইরে পাপনকে কিজে বলবএমন কতা বল্লে যেন আমার মনের হাহাকার দুর হয় শালার বাচ্ছা পাপনের কারনে ক্রিকেট এখন নষ্ট হয়ে জাবে তাই বলতেছি আমাদের যদি কোনু কিছু যায়,1,sports
না খেললে। আমাগ বাল হইব। জানোয়ার। খেলিসনা তোরা। ইতিহাস সাক্ষী খেলা ধুলা দিয়া বিশ্বের কোন জাতি উন্নতি হইতে পারে নাই। শুদু যারা খেলে জানোয়ারেরা। বেশ্যা মাগি নিয়া আরাম আয়েশ করছে। বাঙ্গালী খেলোয়ারের দিকে দেখলে মনে হ এদের নৈতিকতা বলতে কিছু নাই।,1,sports
পাপন জোয়া চোর কেসিনিও পাপন নিয়া আসছে,1,sports
অশিক্ষিত মূর্খ জানোয়ার রুবেল।।।।শিক্ষার আলো তো নায়!!!জানোয়ার।,1,sports
শুয়োরের বাচ্চারা দরলাম গালি দিয়েছে তো কি এমন হয়ছে শুনি জারজ গুলা জার্সি পরা জারজ চামচা টাকে আচ্ছা মত পেটানো যেতো শুয়োরের বাচ্চা চামচার বাচ্চা চামচা লোকটা এত করে বলছে গালি দেয়নি যদি দিয়েও থাকে তাহলে সে তো দুঃখপ্রকাশ করেছে সরি বলেছে আর কি করবে শুয়োরের বাচ্চারা…,1,sports
এক সেঞ্চুরি মেয়েকি বিশ্বের রেকর্ড হয়ে গেল নাকি,1,sports
পাপান তুই শেশ মাদার চোদ,1,sports
পাপন কে জুতা পিটা করা দরকার সাকিব এর মত অভিজ্ঞ খেলুরার কে বহিস কার করে,1,sports
মাদার্চুদ পাবলিক। গালি দিছে ত কি বাল হইছে হাজার মানুষ গালি ত দূরের কথা ভিডিও বানাইয়া আপলোড মারে ওইটা কিছু না।পোলাটারে একা পাইয়া হয়রানি করছে।কুমিল্লার পোলা হইলে চুলকানি কমাই দিত।গাঞ্জাখোর গুলা।🤬,1,sports
"চোদনা,অাসলেই একটা লুচ্চা।",1,sports
শেখ হাসিনা কুত্তার বাচ্চা তুই রাজাকারের শাস্তি তো বেশ ভালো ভালো লোকদেরকে তোর চোখের সামনে এইযে পাপন এক নাম্বারে রাজাকারের বাচ্চা রাজাকারের বাচ্চা জন্য ভালো ভালো প্লেয়ার গুলো নষ্ট হয়ে যাচ্ছে তাদের বিচার কর অমানুষের বাচ্চা তোরা,1,sports
শালা বড় চোর,1,sports
সাকিব দল থেকে বের হওয়া মানি বাংলাদেশ টিম গোয়ামারা খাওয়া বাকিরা বাল ছিরা টাল দিব,1,sports
পাপন কুত্তার বাচ্চা কে বাদ দেওয়া উচিত,1,sports
আরে আচুদারা গাঞ্জাখোর খাংকির পোলারা পোলাডা না হয় মুশি ভাই খারাপই বলছে কই মুশি ভাই তো কিছু বলে নাই মুশি ভাই যদি থাপ্পড় ও দিতো কিছুই মনে করতাম না কিন্তু তুরা খাংকির পোলারা পোলাডারে যেভাবে ধরছস পুলিশে খুনের আসামী রে ও এভাবে ধরে না খাংকির পোলারা ভালো হয়ে যা। চামচিকার বাচ্চারা,1,sports
শালার পো শালারা তোরা জেরা করতেছস না খানকির পোলারা,1,sports
তুই জি ক্যাসিনো খেলছিস সেটার জন্য কি হবে তুই একটা কুততা তোর বন্ধু ও আরেকটা কুততা,1,sports
তদের থেকে রাতের ব্যাশসারা ভালোতদের জন্ন্যই জাহান্নাম রাখা হয়েছে,1,sports
সাব্বির নামের ছেলে গুলোই কুত্তা টাইপ এর।,1,sports
আওয়ামীলীগ ভারতের দালাল। মোদি নির্বাচিত হওয়ার পর একজন লীগ সমর্থককেও দেখলাম না মোদিকে অভিনন্দন জানাতে অথচ সবার আগে মোদিকে শুভেচ্ছা জানিয়েছিলো জামায়াত ইসলাম আর নিজেদের রাজনৈতিক কার্যালয়ে চেয়ারপারসনের বাড়িতে মিষ্টি বিতরণ করেছিলো বিএনপি। অসাম্প্রদায়িক দল কংগ্রেসের পরাজয়ে ছিলো তাদের এই উৎসব উল্লাস কারণ তারা নিজেরাই সাম্প্রদায়িক অথচ আজ তারা মোদির করা আইনের বিরোধিতা করে। মোদির করা আইনের বিরোধিতা করে নুরু নুরু মুক্তিযুদ্ধপন্থীদের ডাকে ভারতের দালাল পাবলিক পিডায় সেই নুরুকে সেই নুরুকে পিডানি দেয়ার কারণে নিন্দা জানায় সেই বিএনপি জামায়াত যারা মোদির জয়ে উল্লাস করেছিলো মিষ্টি বিতরণ করেছিলো সেই নুরুর জন্য নিন্দা জানায় যেই নুরু মোদির বিরোধিতা করে। পাদটীকাঃ মোদিরে চাটছে বিএনপি জামাত বিজাতকে চাটছে নুরু কিন্তু নুরু আবার মোদি বিরোধী নুরু যদি মোদি বিরোধীই হইবো তাইলে বিএনপি জামায়াতকে তাদের কর্মের জন্য মাফ চাইতে কয়না কেন তাদের পা না চেটে? মানে তারাই একে অপরের পাছা চাটতেছে আবার তারাই একে অপরের চনু চাটতেছে মোট কথা পাছা চেটেই হোক আর চনু চেটেই হোক অর্গাজম পাইতেছে এটাই তাদের বড় কথা কারণ উভয়ই সাম্প্রদায়িক। অথচ ভারতের দালাল আওয়ামিলীগ।,1,sports
নাসিরকে কেন খেলায় লয় শালা খেলা পারে না নাসিরকে ফাউ দলে রাখে,1,sports
জানোয়ার খানকির পোলা রোবেল৷ তোর বাবা মা আছে তোর বোন খানকি তোর মা খানকি নিজের পোলা আকাম কিছু কছনা হ্যপি তোমার মজা লাগছে তোমি খায়ছো৷ খাওর৷ সময় খেয়াল ছিলো না,1,sports
গালি দিছে তো কি হইছে আমিও দিলাম খানকির পোল কি বাল ফালাইবি ফালাইছ। হইয়া চ্যাটের বাল হইয়া গেছ্ব,1,sports
পাপন‌ শালা পাগলা হ ওয়ে গিয়েছে,1,sports
খানকির পোলারা চামচামি চোদায় সামান্য জিনিসটা নিয়া নাটক চুদায়😡😡,1,sports
বিসিবি সভাপতি পাপন এর মাইরে কুত্তা দিয়া চোদাই সেই মাকে জইমা সালে বোমা হামলায় মারা গেছে খানকির পোলার মায়েরেচুদি,1,sports
খানকির পোলা তোরা এর মুল হোতা সবার সামনে নাটক করস ওকে সিখিয়ে নিয়ে ছিস ভয় দেখিয়ে,1,sports
নাটক চুদাও তাই না,1,sports
সালা তাসকিন তুই তো দেখি একটা পাগল এটা কন গেইমস হলো নাকি।।। চি চি চি,1,sports
পাপন জারজ সন্তান মাদারচোদ পাপন খানকির পোলা,1,sports
শালারা বেতন ভাতা বাড়ানোর কথা বলছে আর আফগানিস্তানের সাথে হোয়াটওয়াস হচ্ছে। বানচতেরা গুহায় বাশ দিতে হবে। সারাদিন কাইটা মরি টাকা কামাইতে কষ্ট হয় আর মাদারচুদেরা খেইলা কোটি টাকা কামায়,1,sports
পাপন রে জুতা মেরে বাহির কর,1,sports
পাপন খানকির পোলা সাকিব জদি না খেলে বাংলাদেশে তোর কোন বাব খেলবে,1,sports
আরে এটা হল গুজব ছড়ানো খবর এদের খবরগুলো সঠিক না আরে শালা শাকিব যদি ইংল্যান্ডের হয়ে খেলে তাহলে তো ও রাজাকার হয়ে যাবে,1,sports
পাপনের প্লানেই সব কিছু শেষ শুয়োরের সাকিবের ক্যারিয়ার শেষ করে দিলো,1,sports
পাপন শালা এক নাম্বার একটা হারামির বাচ্চা,1,sports
এই হালা রুবেল তুই তোর চেহার আয়নায় দেখেছিস তোকে কেমন লাগে,1,sports
টি টোয়েন্টি খেলার প্লেয়ারদের দিয়ে টেস্ট খেলানো ঠিক ছাগল দিয়ে হাল চাষের মতো,1,sports
মাদারচুদ পাপন তুই ক্রিকেটকে ধংস করে দিছোছ,1,sports
রুবেল জানোয়ার,1,sports
মুসফিকের জার্সি পরা ওই টা প্রকৃত ইয়াবা খোরের মত লাগে ওরে গাছের সাথে বেধে জুতা পেটা করার দরকার সালার পুত এমন ভাব নিচ্ছে যেত ওর বাপ কে গালি দিছে,1,sports
চুদি তোর গুদি,1,sports
রোবেল কে যত টায় গালিগালাজ করতেছে ঐ গুলো মনে হয় রোবেলের শালা হইতে চাইছিল।,1,sports
এ কুকুরের বাচ্চাকে বাংলাদেশ টিম বের করে দেওয়া উচিত,1,sports
গরুচুদা তুই শালা,1,sports
পাপন মাদারচোদের পরিচয় দিল সে যে রাজনীতির কত বড় মাদারচোদ তা আজ শাকিবের সাথে করে সে পরিচয় দিও সে কত বড় খারাপ বাজে লোক আমি মনে করি পাপনের বিরুদ্ধে রুখে দাঁড়ান সবাই সে খেলা নিয়ে রাজনীতি করে বেয়াদবের বাচ্চা পাপন,1,sports
ভারতের সাথে জারা খেলবে তারা হলো পাপন কুত্তা পাপন সুয়র। পাপন জানোয়ার পাপন চোর। পাপন বাইনচোদ। পাপন কুলাঙ্গার চুধন জোয়ারি চুদন,1,sports
এই শালার পো শালা তোর কি না খাইয়া কাম নাই,1,sports
তুই তো মাল খোর তুই কি বুঝবি,1,sports
সালিরে কেমনে মারছস,1,sports
তুই চুর বেটা পাপন,1,sports
ভাই কি আর বলবো কিছুই বলার নাই শুধু এটাই বলবো পাপইন্নআরে যদি জুতা পিটা করতে পারতাম তাহলে ভালো লাগতো।,1,sports
পাপন খানকির পোলারে জুতাদি টানা ঘন্টা পিটানো দরকার,1,sports
সব সালারা দালাল,1,sports
চুদির বেটা চোর।,1,sports
এই দোষ এত দিন কোথায় ছিল।পাপন হালার পোলা। আজ কেন এই কোথা উঠবে।পাপন সালা মানুষ এর চোদা না।।,1,sports
তোমারমাবাবাকেবিকরযকরেঅনেকটাকাবানিযাছোশেখহাসিনাবুঝতেপেরেছেএখনশালাপথছাড,1,sports
মুশফিকুর রহিম এর মত একটা ভদ্র মানুষের গালি দিছে ওরে জুতা পিটা করা দরকার,1,sports
এই ভন্ড শালা চুপক,1,sports
অভার গাজা খাইছা তুইগাজা খোর আবাল,1,sports
মাদ্রাচোত মিত্যা কথা কম বল তর বাপ তো এক জন ভালো মানুষ ছিলেন তুই এমন কুলাংগার সন্তান কেমনে হলে,1,sports
হেপি খুব ভাল চোদন দিছে,1,sports
আগারওয়ালের মারে চুদের।সাকিব তো এমন জায়গায় নামেনা যেখানে খেলা পরিবর্তন করা সম্ভব।সব বিসিবি এর কারসাজি।,1,sports
তোর বোন কে তোর বাবার কাধে তুলে গুয়া মারবো।শালা বেশ্শার ডিম।,1,sports
পাপন রে জুতা পেটা করা উচিত। শালা মাদার দ,1,sports
সালা ডান্ডি,1,sports
লুইচ্ছারা। প্রেম। করতে। পারে। বিয়ে। করতে। পারেনা,1,sports
পাপন মাদারচোদদ হাটাও,1,sports
পাপন শালা তর বাপের টাকা দিছত শালা,1,sports
পাপনের বাচ্চার পদ ত্যাগ চাই। তার এই নিষ্ঠুর বিচার মেনে নিতে পারছি না কিছুতে।,1,sports
কুত্তালীগের ভয়ে গ্যালারি তে দর্শক নাই,1,sports
আরে কুওা বাচ্চা এটা তো হাসিনার নাটক আর বাচ্চা নিয়ে খেলে ওর নাতি নাতনি নাই অন্যের বাচ্চা দেখলে লোভ সামলাতে পারে না কারণ এই বয়সে ওর কেউ নেই এর থেকে বড় অভিশাপ আর কি হতে পারে,1,sports
দূর হালা ভুয়া খবর দেছ,1,sports
ঐ খানকির পো খেয়ে দেয়ে কোনো কাজ পাওনা।। ঐ তোর মায়রে চুদি,1,sports
"মাগী খোর,,,,,,,,, পাগল ছাগল,,,,,,,, তাই সোনার বাংলায় জন্ম নেয়।",1,sports
সালায় একটা মাগি বাজ,1,sports
কিরে খানকির হোলা তোর বোইনের ও তোর মাইয়ারে আনরা বেগ্গুনে মিলি হোন্দাই এই খবর ইউ টিভিতে আপলোড করিদে,1,sports
মাদারচোদেরা সবগুলো দালাল,1,sports
ওরে এখন ফিটিং দিবে এ শালায়,1,sports
বাংলাদেশের খেলোয়াড়রা বাল ও খেলা পারে না শালারা শুধু পারে বউয়ের সাথে ঘুমাইতে,1,sports
এই পাপন এর কারনে বাংলাদেশ এগিয়ে জেতে পারচে না। হালা হারা মি পাপন,1,sports
আইসিসির শালারা বড় ঘুষখোরশালাগো তো আমি কোনো দিন সম্মান করবো না,1,sports
শালা বিড়াল চোখি খুব খারাপ,1,sports
খবরটি আগে দেখিনি এখন দেখলাম। কমেন্ট করলাম আমি গালি দিয়েছি শালারপুত মুশফিক পারলে কিছু করিস,1,sports
মাদারটেক পাপন তুই দেশের ক্রিকেট শেষ করতা ছত ।,1,sports
জানোয়ারের মতো কাজ,1,sports
পাপন কুত্তার বাচ্চা কে অতি তাড়াতাড়ি বহিস্কার করা হুক।,1,sports
গালি দিলে কোন বাল হইবো রে!!!চামচার মায়রে চুদি চামচামি চোদাস সালারা,1,sports
রুবেল ১নং বাইনচোদ,1,sports
মাদারীর বাচ্চা কুকুরের জন্মা<br />বাংলাদেশ বলে সালা বাইচা গেলো,1,sports
সালা বরিশাইলার বাচা 🤬রবি। খানকির পোলা 😡 লোকটা বলো কিছু বলে নাই 😡 তুই বার বার লোকটা রে হাত দরে টানোছ😡 কুতার বাচা😡,1,sports
আরে বোকা চোদা পাপন শোনার ছেলে টাকে চিনলেনা মাদার চোদ পাপন,1,sports
"ছাব্বির হচ্ছে একটি বেয়াদপ খেলোয়ার,,,",1,sports
সালা গুন্ডামি বাদ দে চোর গণ দিবে মানুষ।,1,sports
পুরো বাংলাদেশটাই পাগলাচোদাদের দেশ।,1,sports
সালি একটা মাগি,1,sports
মাদা চুদ পাপন তুই কোনো কথা বলি না কারণ এত দিন এই কথা কোথায় ছিল এখন তুই এসে এই কথা গুলা বলতে আছো কারণ এখন আর কিছু খোজে পাছ নাই দেখে এইটা করছ মাদা চুদ তরে পারলে নিজে খুনি করতাম,1,sports
মাদারচোদ তোর কাজ কি।।।তুই ক্রিকেটে কি করিস।।।তুই তো রাজনৈতিক লোক।।।এতো মাঠ।।কিন্তু খেলা হয় খালি ঢাকা আর চট্টগ্রাম এ।।।তাইলে এতো মাঠ দিয়ে কি বাল ফেলাইছো।। সালা তোর পকেটে কত টাকা ঢোকে জাতি জানতে চায়।। হালা প্রথম শ্রেনীর ক্রিকেট এখনো পিকনিক,1,sports
কিরে তুই কি সাথে চিলিনি হালা গাঁজা খোঁরের বাচ্চা সাসকাইব তোর পুটকি দিয়ে দিমু হালা আবাল ৷,1,sports
তোর বোনেরি চুদি,1,sports
"তর মতো হাজার মাগীর,রুবেলের কাছে সময় নাই",1,sports
সুভা জান আমার কলিজা আমি তোমাকে চুদতে চাই,1,sports
মাদারচদ পাপন,1,sports
মাগির পুলা পাপন তুই একটা কুত্তার চুদা,1,sports
পোলা তোমার সাকিব এর পাশে দাঁড়ানোর কোনো যোগ্যতা নাই তোমার মতো পা কুত্তা রে 👉👌,1,sports
ধুর শালা মাদারচোদের বাচ্চা,1,sports
তোর বৌরে গিয়ে চোদ শালার পুট,1,sports
পাপন সালার পুতের পদত্যাগ চাই,1,sports
তোর মা কে সবাই চোদে,1,sports
তুই মুসফিকের নামে মামলা দে তাহলে দেখবি সব সত্যি বেরহয়ে আসবে তাহলে তেল মারা সব মাদারচুদ ঠিক হয়ে যাবে,1,sports
পোন্দা নাকি পাপোন্দা খানকির পোলা আসলে আপোন্দা 🤣😂,1,sports
পাপন দালাল মাদারচুদ,1,sports
পাপন খানকির পোলা মেইন শয়তান ওরে লাথথী মাইরা বিসিবি থেকা বাইর করা দরকার,1,sports
সিলেটের অধিনায়ক বালের অধিনায়ক,1,sports
মুসপিক এর খবর নাই আর খানকির পোলার গো দালালি,1,sports
ঐ পাগলের বাচ্চা তোর এই ভিডিও বানানো বাদ দে।তোই তো একটা পাগল,1,sports
চোদানি তোই একটা মাগি বিয়ের আগেই চোদা চোদি করছ মাগি তোদের মতন মাগিদের জন্য জাতীয় দলের খেলোয়ার রা ভাল খেলতে পারেনা,1,sports
পাপনের পুটকিমারি চুতমারানি পোলা,1,sports
পাপনের মায়রে চুদি,1,sports
পাপনের জিরে চুদুম,1,sports
এই বুড়া জাহিল জঙ্গী জানোয়ার কে সাক্ষাতকার নিল।সাংবাদিকদের খাইয়া কোন কাজ নাই। বেকার কি করব।,1,sports
সাওয়ার বাল পাপন,1,sports
সালার গাজা খোর,1,sports
নাটক চোদাও না,1,sports
তোর পুটকি দিয়ে গরম ডিম দেয়া লাগবে শালা,1,sports
সাব্বির বাংলাদেশ ক্রিকেট কে কি দিছে। পাছায় লাথি মেরে হাতে হারিকেন দরায় দেওয়া উচিৎ।,1,sports
বালের প্লেয়ার,1,sports
শালারা পাগল,1,sports
পুরান কথা বলার কি দরকার?,1,sports
তর বাবা মরছে মাদারচুদের বাচ্চা,1,sports
পা পোন্দা তুই বাংলাদেশ ছাইড়া ভাগ শালা,1,sports
তরে চুদি তর বোনকেও চুদি,1,sports
পা পুন্দাকে চুদি,1,sports
প্রথম দাবী দেওয়া দরকার ছিলএই বাইনচোদ এর পদত্যাগ তাহলে সব সমাধান হয়ে যেতো,1,sports
গালি দিছে তো কি হয়েছে অন্যায় করলে পুলিশ আছে দেশে আইন আছে তোরা খানকির পোলারা ছেলেটার সাথে এমন আচরন করলি কেন পুলিশ খানকির পোলারা কি করছিল,1,sports
টা তো বাল মার্কা ছিলো। খালি খেলোয়ারদের দোষ দিয়ে লাভ নাই। যে অযোগ্য তাকে দলে ঠাই দিলে এরকমই হবে,1,sports
"অই কাইল্লার বাচ্ছার মার সাথে অরে ঘুমাতে দেওয়ার দরকার ছিলো,, অয় অর মার সাথে সেক্স করলে অন্ন নারির সাথে এমন করতে পারত না,, এই সব মাদার চোদরা হইছে ঝারত সন্তান,, ১০ জনে চুইদা অদের কে বের করছে,,এই জন্নই মেয়েদের সম্মান নিয়ে এমন খেলা করে,,,",1,sports
ও আমার বালের খেলুয়ার মাদারচুদ,1,sports
নুরু হইলো চোরা😂😂 তুমি হইলা ভাল🤔🤔 ভাষণের আঙ্গুল তুলতে গিয়া👆👆 চোদর আঙ্গুল তোল 👃👌 হায়রে কপাল হায়রে কপাল কি যুগটা আজ আসলো? গাধার মত জ্ঞান নিয়ে বিশ্লেষণে বসলাে 🤮🤮 নূরুর মত হীরকখণ্ড বুকে টেনে রাখবো💎💎 তোরমত জুতোকে আমি পায়ে পরে থাকবো🥾🥾,1,sports
গাজাখোর শালা,1,sports
ধারাভাষ্যকার শোনে আমার পছন্দের একজন শিল্পের এটিএন বাংলার চেয়ারম্যান মাহফুজ স্যারের গান মনে পরে গেল যে বাল তুমি পালাইতে পারবনা সেই বাল নিয়া তুমি থাকো কেন বাল চোদা আবাল জাতির পোলাপান,1,sports
মুশফিকের গুষ্টিরে চুদি শালা আবাল চোদা কোথাকার কে জানে,1,sports
মুসফিক কোন চেটের বাল যে গালি দেওয়া যাবে না খারাপ খেলছে গালি দিছে বাছ এতো চামচামির দরকার কি,1,sports
উনি তো বলতেছে যে গালি দেইনাই তার পরেও জানোয়ারের বাচ্চারা লোকটাকে ছাড়ে না,1,sports
"জুতো মার সালার মুখে শুয়ার বাচ্ছা , খেলা থেকে বার করে দেওয়া উচিত .. শালা বিরাট কে নিয়ে উল্টো পাল্টা যখন বলছিলি সুইয়ার গুলো , তোদের দেশের প্লেয়ার কি রে",1,sports
গালি দিলে কি হইছে খানকির পোলারা,1,sports
আসলে কম পানির মাছ বেস পানিত পরলে জা হয় আসলে এক টা আবাল সালা,1,sports
গাছে কাঁঠাল গোঁফে তেল এর বাচ্চারা সব জানোয়ার,1,sports
ফালতু পাগলার বেটা আমীা মজা করার জন্য এগুলো করা উচিত নয়,1,sports
জার্সি পরা ছেলেটা কে ফকিন্নির বাচ্চা ফকিন্নি থাকবি যত চামচামি করস নাই কেন মাদারচোদ তোরে পাইলে আমি জবাই করতাম এখানে ছেলেটা কোন বকা দেয় নি তারপরেও ছেলেটাকে হয়রানি করাতেছে,1,sports
এই তাসকিন তুই কি মানুষ না অমানুষ জানোয়ার কুকুরের বাচ্চা।,1,sports
পাপন যে কত বালা তা একটু পিছনে দিগে তাখালেই বুজা যায় কত বড় চালবাজ মাদার চুদ,1,sports
পাপন কুত্তার বাচ্চা এিকেট দলটাকে ধংশ করতাছে,1,sports
তুর পা ছাটা কুত্তা!!,1,sports
খানকির পোলা শান্ত বেকা চুদী কোন সময় রান করতে পারে না খুলনার মায়েরেচুদি মাগির পোলা শান্ত তোর মায়েরে চ ঢাকা লাভ ইউ খানকির পোলা খুলনা শান্ত তোরে বলতেছি রাজশাহীর সাথে কত ভাল খেলিস তা দেখবো মাঙ্গের পোলা,1,sports
তুই ই সব জানো বাইঞ্চুদ।তুই তারিখ বললি স্পট পিক্সিং সামনে আসতেছে।আর এখন বলস দিন আগে শুনছস।আগে কিছুই জানতি না।আমাদের মদন পাইছস???,1,sports
রান্ডিয়ার মায় রে চোদ,1,sports
তাসকিনকে জুতামারা উচিত,1,sports
রুবেল কুত্তা<br /><br />্্,1,sports
পাপনদার জন্য আমার পায়ের জুতার বারি কারাকারা একমত,1,sports
বাংলাদেশ উপরের যারা কর্মকর্তা আছে সকলে খানকির বাচ্চা খানকির বাচ্চারা চায় সব কিছু ধ্বংস করতে,1,sports
বাইনচোদ মাশরাফির দিন শেষ রাজশাহীর বাংলাদেশ 🇧🇩,1,sports
রুবেল খানকির ছেলে তোর মারে চূদি বেশ্যার বাচ্চা জারজ সন্তান তুমি আল্লাহকে গালি দেস,1,sports
পাপনের কুত্তার বাচ্চাদের হাত আছে!! এখন কি তর বৌ আর মেয়ে নিয়ে খেলিস শালা পাপনের বাচচা !! বানচুদ,1,sports
পাপন মাগীর পোলা ষডযনত,1,sports
তগ কি কুত্তার দল বকা দিসে ভাল হইচে,1,sports
গ্যালারী তে দর্শক মুশফিক কে চুদতে ও পারে। এগুলো মেনে নিতে পারলে মুশফিক খেলুক। নয়তো ওর খেলার দরকার নাই।,1,sports
বালকামা রা বাল খেল,1,sports
ওয়াটসন আমার ধনও খেলা পারে না হুদাই হালায়।,1,sports
"শুধু সাব্বির বেয়াদপ না পুরো ক্রিকেট টিমটাই বেয়াদব /বেত্তমিজ .....এই আস্তে , এটা আমার কথা না । এটা ভারতীয় মিডিয়ার কথা । সালার বাঙালি হয়ে বাঙালিকে গাইল্লাইতে ইচ্ছে করে । ভিডিওর শিরোনাম দেখে মনে হয় সানিয়া তাদের খালাম্মা লাগে !! সাব্বির সানিয়াকে কি বলেছে সেটা নিয়ে লাফাচ্ছে , সানিয়া সাব্বিরকে কিবলেছে সেটা বলতেছেন না কেন ?",1,sports
নিচতলা ঠিক আছে নি বিয়ে যে বসবেন আর তোমার মতও মাতারি কে কােন আবাল বিয়ে করবে,1,sports
তার সেঞ্চুরী উদযাপন নিয়ে খারাপ কিছু দেখি না। কিন্তু সে ড্রেসিং রুমের দিকে তাক করে করবে কেন।,1,sports
এই দালাল নাসির কি তোরে কত টাকা দিছে। না তোর বোনের জামাই লাগে ।আর মাগিরা তালি মারে তোদের ঘোরার সোনা দিয়ে চোদার দরকার।,1,sports
এই কুত্ত আগে জানলো কেমনে,1,sports
তুই তো একটা শয়তানের বাচ্চা মিথ্যা নিউজ দেশ শয়তানের বাচ্চা,1,sports
পাপন একটা মাদার চোদ 😡,1,sports
বলেছে তাকে ছেড়ে দাও । সব পাগল ।,1,sports
তোর মারে চুদি মাগির ছেলে তোর কচি বোনরে চুদি তোকে পাইলে জুতা দিয়ে পিটাব,1,sports
সাকিব কে একটা কাগজ হাতে ধরিয়ে দিয়েছে। কাগজ টা পড়তে কতটা কষ্ট হচ্ছিল ওর সেটা কি সামনে থাকা লোকগুলো দেখেনাই? আর পাপন জানোয়ার তোর রাগে কার কি আসে যায় রে? তুই ই সবচেয়ে বড় শয়তানের মূল।,1,sports
তুই পদত্যাগ কর সালা পাপনআপনার তার কথায় কান দিয়ে খেলোয়াড়দের খারাপ ভাববেন না কারণ ওর ও অনেক দোষ আছে অপেক্ষা করুন চলে আসবে সামনে,1,sports
"বাংলাদেশের সব ক্রিকেটার সব বাইঞ্ছদ
",1,sports
খানকির পোলার দেশে মাগির পোলার বসবাস দুই বছর পর আইসিসির বাচ্চা বাহির হলো,1,sports
তোমাকে কুত্তা দিয়ে চুদানো উচিৎ বেশি কিছু বললাম না,1,sports
বাইন চোদ করে কি জুতা মেরে কপালে দাক করে দেওয়া দরকার গুলোরে এক নাস্কি গালি দিছে আমাদের রাসুল গালি দিলো এট পতিবাদ করে না কি বলবো,1,sports
পাপন খানকির পোলা তোর পদত্যাগ চাই,1,sports
সালা আবাল চুদা।। বলদের মত কথা!; একসময় বাংলাদেশের স্পিন সেরা ছিল এখন বাংলাদেশ থেকে আফগানিস্তান পাকিস্তান ভারত স্পিনে ভাল।।তাইলে আপনারা কি ভাল ফালাইতাছেন?? বাংলাদেশ স্পিনের উন্নতি না হইয়া অবনতি কেরে??,1,sports
খানকির ছেলে তোর মাকে চুদি।,1,sports
এই চামচা সালা হাত ছার,1,sports
গালি না হয় দিছে কি হইচে ভারতের খেলোয়াড়দের ঘড় বাড়ি পুরাইয়া ফেলে কিছু করতে পারে না অার গালি দিছে বিচার করতে অাইছে সালার বাটপার সব।,1,sports
কুত্তার বাচ্চা তোর মুখ আর দেখতে মন চায় না,1,sports
সাকিব ছাড়া বাংলাদেশ অচল পাপন খানকি পোলা তুই পদতেগ চাই,1,sports
আরে খানকির পোলা শাকিব তোকে বলছে আমি ওয়ার্ল্ড কাপের ভালো খেলছি আমার টাকা বোনাস গুলো দিয়ে দেন ।কেন বলা লাগবে তুই নিজে থেকে দিতে পারোস না মাদারচোদেরা রাজনীতি তো দেশটাকে ধ্বংস করে দিয়েছে বাকি ছিল খেলাটা ওটাকে তোরা ধ্বংস করে দিবি খানকির পোলারা,1,sports
পাপন মাগির পুলা,1,sports
চামচা গুলো জুতা দিয়া পিটানো দরকার,1,sports
সাবার ম কাথা হলো পাপনের পদত্যাগ চাই। আর মাদারচোদ পাপনের বিচি কাইটা দেওয়া হোক😡😡😡,1,sports
এই মাদার ছুদের বাচ্ছারা সাধারন মুশফিকে গালি দিছে ওকে দরে নিয়ে গেছিস আর আমাদের নবীকে নিয়ে কুটনিতী করে তাকে কিছুই বলে না শালার কি যে বলবো তদের ভাষা খুঁজে পাইনা,1,sports
তোর রাগের মায়রে চুদি পাপন খানকির পোলা তোর হাতে হারিকেল দরাইয়া তোর মায়রে চুদমু খানকির পোলা,1,sports
গাড়াগ্রাম পৃথিবীর অনেক খেলোয়ার আর দর্শকদের যে ইতিহাসে যত তগুলোতে খেলা দেখে ভালো করে দেখ যে সেখানে কত কিছু ঘটে যায় তাড়াত কিছু বলে না আর তুই সামান্য একটা বিষয় নিয়ে ওই জার্সি পরা যে জানোয়ারের বাচ্চা গাঁজাখোর লোকটা কেমন ভাবে ধরছে যে পুলিশ এভাবে ধরে না গাঁজাখোরের বাচ্চা শাস্তি চাই ওরে ওখান থেকে সারা জীবনের জন্য বের করে দেয়া হোক ওর মুখ জানে আর কেউ না দেখে ওর সাথে সাথে যারা জড়িত ছিল লোকটাকে হ্যাঁ নাস্তা করছে ওই চামচা গুলো খেলোয়াড়দের বদনাম হয়,1,sports
মাদার চুদ,1,sports
এগুলো কি কুত্তা নাকি সেই লোকটা বলতেছে আমি গালি দেন এই কুত্তার দল বলতাছে গালি দিলেন কেন,1,sports
সাওয়া বনাম হোল আবাল চুদা এডমিন গাজার ডেট অভার হয়ে গেছে মনে হয়।,1,sports
পোলা তোর মাইয়ারে চুদি তোর পালিয়ে চুদি,1,sports
পাপন একটা বাহিন চোদ,1,sports
রফিক কুত্তার বাচ্ছা মুসফিক এর পা চাটা কুকুর,1,sports
যিনি লোকটার হাত পিছন দিয়ে ধরছে ওই শালারা বাইন্ধা গুয়া দিয়ে গরম ডিম দেওয়া দরকার।,1,sports
পাপন মাগির পোলা,1,sports
গালি দিছে ঠিক আছে তার ভুল হইছে তার জন্য বলছে তারপর অই মানুষটারে জা তা বলতাছ সালা মাদার চোদ জারা এই টা তুইলা ছারছে তারা হইল মাদার চোদ,1,sports
বাংলাদেশে পাপন সাহের মত লোক মিনিটে পয়দা করা জায়।কিন্তু সাকিবের মত ক্রিকেটার বছরে টা জন্ম হয়েছে। তাই সবাই সাকিবকে সবো;চ্চ সন্মান দিচ্ছি। পাপনের সমস্যা কোথায়????পাপন সাহেব আপনাকে বলছি আপনি যদি বিচিওয়ালা হয়ে থাকেন সাকিবের মত প্লেয়ার বানিয়ে দেখান।,1,sports
এই বেশ্যার জন্য ইউ‌টিই‌বে আশা দায় হ‌য়ে‌ছে।,1,sports
থ্যাঙ্কস টু ইউ তাসিনেশন ভাইয়া ❤ভিডিওটার মাধ্যমে বাংলার মানুষকে বুঝিয়ে দেওয়ার জন্য যে পাপন ইজ এ নাম্বার ওয়ান মাদারচোদ কা বাচ্চা 😡আর শাকিবিয়ানরা প্লিজ দ্রুত ভিডিওটা শেয়ার করে সবার মাঝে ছড়িয়ে দাও 🙏🙏,1,sports
পাপন কুত্তার বাচ্চারে লাথি মারতে মন চায়,1,sports
শালার পুত পাপন 😡,1,sports
সব কিছুরই পিছনে পাপন দায়ী শালা চোরদূর্নীতিবাজ!!,1,sports
ছাগলের বাচ্ছা রুবেল,1,sports
পাপন খানকির পোলা একটা ভারতের বীজ,1,sports
সালা জারজ,1,sports
শালাদের কাজ নাই তো চামচামি করে খাই,1,sports
তোর মত হারামি না থাকলে খেলায় কোনো সমস্যা হবে না কিছু একটি খেলোয়াড় যুদি না খেলে দেশের অনেক বড় ক্ষতি হবে,1,sports
দেব তো খাকির পোলা৷ দালালের মাকে চুদি৷,1,sports
জার্রসি ওলা সালাটা ফেমাস হতে চায়ই,1,sports
হায়রে কুত্তার বাচ্ছারা এটা স্বাধীন দেশ মন্তব্য করার অধিকার সবারই আছেন। বান্দির বাচ্ছা রা মাদারচুদেরা যারা আমার নবী কে গালি দেয় তখন কোথায় থাকিস কুত্তার বাচ্ছারা।।,1,sports
পাপন কুত্তার বাচ্ছা কে জুতা মার,1,sports
খাটে খেললে মাঠে কি বাড়া খেলবে,1,sports
পাপনের দুই গালে জুতা মরো তালে তালে।,1,sports
মাদারচোদের দল একটা সাকিবের বাল একশ পাপনের সমান,1,sports
বেইমান সালা,1,sports
ওরে জাতীয় দল থেকে বের করে দেওয়া উচিত শালা বসতির ছেলে,1,sports
নাছিরের পাছায় থুতু ও এক লাথি দিয়ে দল থেকে বের করে দেয়া উচিত।,1,sports
মাঠে দেখা যাবে কী বাল ফালাও,1,sports
পহিন্নির পোলাপাইনের বাত হলে যা হয়,1,sports
এটা কোন ভাল মানুষের কাজ না ওরা সকলেই জানোয়ার,1,sports
মুশফিক কোন বাল গালি দিলে কি এমন ক্ষতি হলো সালারা সব টাকার জন্য খেলে,1,sports
মুশফিক ও মাহমুদউল্লাহ কে বাদ দেওয়া উচিৎ। দুই জন বড়ো মাদারচোদ মিরাজ কে কোন যোগ্যতায় আছে বুঝি না। সাকিব একা সব করতে পারবে না। মুশফিক রানে আউট হয়সে কিসের ব্যাটসম্যান।?,1,sports
হালা ফালতু নিউজ করিস কেন,1,sports
এই মাদার চোদ গানজা খোর সেতো ভুল শিকার করছে তার পর কেন এতো বারা বাড়ি মাদার চোদ,1,sports
জার্সি পইরা যেইডা দইরা আছে শালার পুত কি পাট নিছে খানকির পুতের পাট দেইখা বাছিনা দেইখাই মনে হইছে হালা গাযা খাইয়ে আসলো,1,sports
এই রাগেই সালা পাপন সাকিব কে নিষেধ করেছে।। এর মত মালাউন যারা আছে বোর্ডে সবার পদত্যাগ চাই।।সবাই একমত।,1,sports
"বাংলাদেশী সাংবাদিকদের একটি বিশেষ গুন হলো, মূর্খতার মাধ্যমে নিজ দেশেরই হোগা মারা",1,sports
সালায় একটা গ্রেট মাদারচোদ,1,sports
বাংলাদেশে খেলোয়ারা সুযোগে সৎ ব্যবহার করেছে।। বিশ্বের অনেক দেশ তাদের খেলয়ারদের এত সুযোগ সুবিধা দিতে পারেনাদেয় না।।। ওরা শুধু টাকার জন্য খেলেদেশ ও জাতির জন্য না৷৷ আমি চাই বাংলাদেশের ক্রিকেট খেলোয়ার বিচারের আওতায় আনা হক।।।।। মাদারচোদ সব।।,1,sports
বাগে পাইলে ক্যাটরিনারেও ছাড়তনা আমাদের এই লিজেন্ড সাব্বির।ভাগ্য ভাল ক্যাটরিনা বাইচ্যা গেল......,1,sports
তাসকিন একটা পাগল ওই দুইটাও পাগল।,1,sports
নবিরে গালি দিলে তার কোন বিচার হয় না 👿👿👿আর কোন হান কার বালের খেলোয়ার মুসফিক তারে গালি দিলে সমস্যা তোর মুসির চোদ্দ গুস্টি চুদি খানকির পোলা,1,sports
পুটকি মার ।তার অপরাধ টা কি ছিল দেশবাসী এতো সচেতন জানতাম না,1,sports
জার্সি পরা মাগীর ছেলেকে ঘন্টা পিটানো হক সাকিব কে ওর আব্বা অকারনে বাদ দিছে। তা নিয়ে কিছু হয় না আর সাধারন পাবলিক কে ধরে গালি দেওয়ার খানকির ছেলে,1,sports
পা পোন্দা পুন্দি মাদারের চোদ😠,1,sports
সাকিব ছাড়া আমাদের ক্রিকেট এর আলো হারিয়ে যায় আকরাম খান পাপন কোনো হালায় কিছু করতে পারে নাই সাকিব এ দেশের ক্রিকেট কে একটি ব্র্যান্ড এ পরিণত করেছেন,1,sports
টাকা পয়সা হলে মানুষ এরকম করাটা স্বাভাবিক টাকার গরমে এরকম করছে,1,sports
মাগির পুত তোর বউরে চুদি চুদার খবর দিস,1,sports
সালার পুত,1,sports
যখন কুমিল্লায় ছিল তখন বাল ও ছিরতে পারে নাই ইম্রুল কায়েস,1,sports
পাপন সাহেব দেখাই দিলেন উনিও বাঘতয় এই বাঘটার বয়স হইসেবিচিতে জোর নাইসেটাও বুঝতে হবে।,1,sports
তুর মারে চুদি টাইম নস্ট করলি কেন।,1,sports
"উদের মতো লুচ্চা মার্কা প্লেয়ার দের কে পাছায় ট্রস ট্রস কইরা গরম লোহার বারি দিতে পারলে ভালো হয়তো, ফইন্নির পোলার নাম মিয়া খা, অল্প পানির মাছ বেশি পানিতে পরলে যা হয় আরকি,",1,sports
মাদারির বাচ্চারা বাল খেলছে,1,sports
ছাগীবালাছান খানকির পোলা,1,sports
পাপন একটা মাদার চোদ শালার পুটকি দিয়া গরম ডিম ঢুকানো দরকার সাকিবের কিরিয়ার নষ্ট করার পাইতারা😡😡,1,sports
পাপন এক টা মাল,1,sports
ক্রকেটাররা কি বাল ছিরছে। দেশকে কি খেলা উপহার দিছে। এমন হোত যে এত ভাল খেলতাছে সোনার টুকরা ছেলেরা তারপরও কোন সুবিধা পায়না। তাইলে তাদের কথা ঠিক ছিল।,1,sports
মাগির পোলা মুশফিক,1,sports
এই নুরু মাদাচুদের মত মানুষ আমি লাইফে দেখি নাই আপনি সামনে কোন মুভি ভানাইলে ওরে ভিলেন হিসেবে নিয়েন শালার প্রতিভা আছে,1,sports
কেউ মরে দুঃখে আর কেউ সেইটা পুজি কইরা কামাইয়ের ধান্দা করে।আবাল পুলেপান।,1,sports
মুশফিক কি বাল ফালানো মুসা,1,sports
রুবেল মাদার চোদ,1,sports
পাপন্না হে একটা দালালের বাচ্চা,1,sports
তোর বিচিতে গুল্লি করা দরকার মালুর বাচ্চা,1,sports
পাপন এ গাজা এবং মদ খায় ।আমি নিজে দেখেছি ও আমার কাছে ভিডিও আছে ! কিন্তু আমি তা পাবলিক করলে আমার ফ্যামেলি সমস্যা করবে বলছে !!!হি ইজ মাদার ফাকার !!,1,sports
এই খানকি খুনকির লেইগা পোলাপাইন<br />গুলা খারাপ হইতাছে<br />পিডা সালিরে,1,sports
হে যুবসমাজ সবাই আন্দোলন শুরু করুনযাতে কুলাংগার পাপন পদত্যাগ করে আর সাকিব মাশরাফি মুশফিক সবাই যেন খেলায় ফিরে আসে নয়তো ক্রিকেট খেলা দেখা বন্ধ করে দিন।আমরা রাস্তায় নেমে প্রতিবাদ আন্দোলন না করতে পারিসোশ্যাল মিডিয়ায় তো করতে পারি।তো আর দেরি কেন? মোবাইল হাতে নিনএখন থেকেই শুরু করুন আপনার প্রতিবাদ আপনার আন্দোলন। জানিয়ে দিন আপনারা বাঘের বাচ্চা সাথে আছেন ক্রিকেটার বাঘদের সাথে কুলাংগার চতুর শিয়াল নেকড়ের বাচ্চা পাপনের সাথে নন।,1,sports
সাংবাদিক সব মাদার চোদ পাপন চুর এর পদ্যতেগ জরোরী দরকার,1,sports
পাপনের দুই গালে জুতা মারি তালে তালে।😡😡😡একটা লাইক👍 একটা জুতা,1,sports
মুশফিকের মায়রে চুদি সাথে ঐ ওভির মায়রেও চুদি😠😠,1,sports
মাগির ফুয়া পাপন তর মারে সুদি,1,sports
সাব্বির ও নাসিরের মত মাগিকোর,1,sports
পাপন জুয়ারীর গালে জুতা মারো তালে তালে শালারে বিসিবি থেকে ঘার ধরে বাহির করে দাও নাহলে বাংলাদেশ ক্রিকেট দলকে শেষ করে দেবে।,1,sports
সব কিছুর মূলে আছে পাপইন্না।শালা পাপনকে বিসিবি থেকে গার ধাক্কা দিয়ে বের করে দিলেই হবে।ক্রিকেট ধ্বংস করার পায়তারা!!!!,1,sports
ভারত কোন দিন ও বাংলাদেশের ভালো চায়নি। ওরা সব সময় ধংস করার জন্য চেষ্টা করে। সেইটা রাজনৈতিক ভাবে হোক কিংবা অত্যনিতিক ভাবে হোক। আমি ধিক্কার জানাই ভারতীয় দালাল দের। আমি আর ও ধিক্কার জানাই আমাদের দেশের ভারতীয় পা চাটা কুত্তা দালালদের কে,1,sports
"শালা একটা মাদারচুদ
",1,sports
এবা পাপন তুই মাটে খেলবি সালা বান চুদ,1,sports
শালার পুত। তুই মর,1,sports
চুতমারানি মাদারিরা তাড়াতাড়ি পুরো ম্যাচ একসাথে দে এত দেরি করো কেন?,1,sports
"শালা গুবেল, ঠিক মত কথাও চুদাইতে পারে না বাইনচোদে। শালা মাদার ফাক্কার রুবেল।",1,sports
সালের অক্টোবর পযর্ন্ত সকল প্রকার ক্রিকেট দেখা বন্ধ। সালা পাপন মাদাচোদ কে লাথি দিয়ে বের করে দেওয়া হক।,1,sports
মোসাদ্দেক এই কুলাঙ্গার যে দলে খেলবে সে দলে যদি শচীন টেন্ডুলকারও থাকে তবুও সে দল হারবে। শালা ইনজুরিতে পরেনা কেন এই আবাল? না পারে বল না পারে ব্যাটিং।,1,sports
এই কুলাঙ্গারপাপের পাপন কে জুতা পিঠা করে বিসিবি থেকে বের করে দেওয়া হোক,1,sports
চোর হালার পুত,1,sports
পাপন হালায় করচে টা কি অই হালার ফাসি চাই। একটা কেরিয়ার নস্ট করল,1,sports
জাতীয় দলে খেললে বালও ছিরতে পারবে না সবার জানা আছে,1,sports
পাপন মাদার চোদ তরে যদি চুতা দিয়ে পিটাইতে পারতাম,1,sports
পাপন তুই একটা মাদারচোদ তুই নাটের গুরু,1,sports
নুরু মুরগী চোর সেটা ঠিক আছে কারন সব কয়টাই এক গোয়ালের গরু কিন্তু ছাত্রলীগ কে নিয়ে কিছু বল্লেন না কেন?নুরু জদি চোর হয় তাহলে ছাত্রলীগ হচ্ছে চামার কারন এই গুলা লেখা পড়া করতে জায়না এই গুলা ভার্সিটি যায় সাধারন শিক্ষার্থীদের পুটকি মারার জন্যে ।,1,sports
পাপন কুকুরের বাচ্চারে জুতা মেরে দেশ থেকে বের করা উচিত,1,sports
সাব্বির কে যারা গালি দিবে taderke আমি চুদবো,1,sports
চামচা শালারা তোমরা এরকম করচ কেন।,1,sports
পাপন এর দুই গালে 👞জুতা মারো তালে তালে👟,1,sports
হালার ফুতেরা মুসফিক যদি গালি শুনে থাকে তুমার ভাবারে যে পাশে চিল তারা শুনত না,1,sports
হ্যাপিরে সেই সুদা সুদিছে রে,1,sports
শালা পাপন তুই বেশি বারছো🤬🤬🤬🤬🤬,1,sports
খেলার মারে চুদেছে,1,sports
বাংলাদেশের প্রধানমন্ত্রী যেমন ইন্ডিয়ার সাথে হাত মিলিয়ে দেশের ক্ষতি করছে। তেমনি এই শালা কুত্তার বাচ্চা ও রেন্ডিয়া এর সাথে হাত মিলিয়ে বাংলাদেশের ক্রিকেট নষ্ট করছে। আমারা সবাই ওর পদত্যাগ চাই ।,1,sports
ইমরুল কই হালা? তোদের সিলেকশন এর মারে বাপ ।,1,sports
বিছিবি সালারা বসে বসে গাজা খায়,1,sports
কিরে রুবেল কে কয় বার চুদা দিল মাগি বিয়ে করে কি হবে বিয়র আগে চুদা দিরে দিল,1,sports
শুধু চেহারা সুন্দর হলে ভালো মানুষ হওয়া যায় না সুন্দর চেহারার মাঝে অমানুষ কুলাংগারের প্রতিচ্ছবি মানুষ নামের অমানুষ তাসকিন !!! ছিঃ ছিঃ ছিঃ ছিঃ ছিঃ ছিঃ ছিঃ( মা বাবার কাছ থেকে ভালো,1,sports
সাব্বির একটা মাদারচোত,1,sports
এই নায়লা নাইমের সাথে অশ্লীলতার কারনেই আজ সাব্বিরের পারফরম্যান্স এত খারাপ,1,sports
পাপন হারামি,1,sports
কোন নডির পুত এইর ধরনে ভিডিও বানাছ অামি যদি তদের পায়াই তাহলে মারব,1,sports
তুই চুদির ভাই গাজা খাইছদ নাকি,1,sports
বাইনচুদ তুর বিচার হবে কবে?????,1,sports
হালা টেকনিক্যালি কথা বলছো জাতি বোকা না সবাই সব বুজে। হাজার কোটি টাকা আকরে দরে আছো এখন মিঠা মিঠা কথা বলে মানুষ কে বুজাইতাচো তুমি দোয়া তুলসি পাতা।,1,sports
পাপন মাগির পুত তুই পদত্যাগ ল সব ভালো হয়ে যাবে,1,sports
সবকাকি।পোলা।গাজাকুর।পুলিশ।কিবাল।পালার,1,sports
পাপন সালাকে বাদ দিতে হবে,1,sports
হাইরে বাইনচোদ মিথ্যুক মাগিরপুত দুইদিন আগে বলছিলি সাকিব অনুমতি না নিয়ে বিজ্ঞাপনে কাজ করতে গিয়ে অন্যায় করেছে আইন ভঙ্গ করেছে। তাকে নিষিদ্ধ করা হবে।আর এখন আইসিসি নিষিদ্ধ করছে আর মায়া চোদাস মাগিরপুত।বছর আগের ঘটনা এখন আইসিসি কিভাবে জানলো সেটা বাংলাদেশের মানুষ বুঝে গেছে,1,sports
হালায় গাঞ্জা খায়া আইছে,1,sports
পাপনের পাছা দিয়া টাকা দামের আছুলা বাঁশ দিতে চাই,1,sports
সাকিবের বাল গুলো ছিরো তোমরাক্রিকেটের মাইরে চুদি পাপনের মেয়েরে চুদিনান্নির বউরে চুদিআকরামের খালারে চুদি,1,sports
তাসকিন কে খুব ভালো মানুষ মনে করতাম আসলে সে একটা পাগল,1,sports
মাদারচুদ রা আজাইরা ভাব চুদায় বালা ফালাইছে পুলাটারে অসহায় পাইয়া কি ভাব!!,1,sports
পুটকি মেরে একদম ছিড়ে দিবো খানকিরপুতটাকা কি তর বাপের যে পাকিস্তানের সমতকের জন্য কোটি টাকা সালা খানকির পশু,1,sports
তুমি আমার বাল,1,sports
কামলাচোদারা মুসফিক নিজেও এমন করতো না।খানকিরপোলারা এই মুসফিক আজ মুসফিক হয়েছে আমাদের মতো পাবলিকের কারনে।ছেলেটা ছরি বলছে তারপরও তাকে এতো অপমান মাদারচোদের বাচ্চারা!!,1,sports
পাপন খানকির পুলারে জুতা দিয়ে পিটাইলেও আমার জুতার অপমান করা হবে,1,sports
মুশফিকের মারে চুদি,1,sports
পাপনের মারে চুদি এইটা সাজানো,1,sports
বাল পাপনের বাল ছিড়বা দেইবেতন আরও কিছু বাড়াইদেই 😂,1,sports
পাপন খানকির পোলারে জুতা দিয়া পিটানো দরকার।,1,sports
তুই তু কুত্তার বাচ্চা তুই করতেছিচ,1,sports
মাদারক্সোদ তোর এতো বড় সাহস,1,sports
ভুল তথ্য না দিয়ে ভালো হয়ে যাও সময় আছে তোমার মত বালের শিক্ষিত বাংলার মানুষ চাই না ভুদাই তুমি তো ভালো করে কথা বলতে পারো না বুকাচুদা কুরআন নিয়ে বারাবারি করো না ফালতু ইউটিউবার,1,sports
সাব্বির কে দেশি কুকুর দিয়ে চুদানো দরকার,1,sports
"আমি অন্তত খুশি । সাব্বির তো অনেক চাপের মধ্যে ছিল, এইজন্য এই রকম উদযাপন করছে সেঞ্চুরি করে । সমালোচনা না করে ওকে আরো সাহস দেয়া দরকার যাতে সামনে বিশ্বকাপেও ভাল করতে পারে ।",1,sports
আমাদের এলাকায় একটা বানর বাচ‌চা দিয়েছে। বাচ‌চাটা অন্য কোন বানরের বাচ‌চাকে কিছু খেতে দিতে চায় না। বানরের বাচ্চাটার চেহারার সাথে একজনের অদ‌ভুত মিল রয়েছে যার নাম পাপঅন। তাই আমি বানরের বাচ‌চাচাকে পাপন বলে ডাকি।,1,sports
জুতার মালা পরাইয়া ওরে দল থেকে বের করা হোক,1,sports
জার্সি পরা গাঞ্জাখোর এর মাইরে চুদি,1,sports
তোর মায়রে চুদি,1,sports
জনি টা মাদারচোদ ও একটা এর মালিক সালায় একটা মাদারচোদ সাথে তাসকিন হলো মাদারচোদ রোজা রেখে এমন করতেছে,1,sports
এগুলা করে কি লাব তোর কুত্তার বাচ্চা,1,sports
এগুলা তো সবাই জারজ। পুলিশ কোথায়। মুরফিকুর টাকা দিয়ে কিছু গাজা গোর পালন করে।আজ বুজাই গেল।,1,sports
খানকির ছেলে পাপন।,1,sports
ও একটা বেয়াদব নাম্বার 1,1,sports
এসব কুত্তার বাচ্চাদের কেন রাখা হয়।,1,sports
ভুজকির পোলা তোর মা বোন কে মানুকে দিয়ে চোদা মজা পাবি,1,sports
তোরে চোদার দরকার,1,sports
সালারপুর কি লিখলে আর কি দিলে,1,sports
আমার বালের খেলোয়াড়,1,sports
তার মারে বোনরে তারে সবগুলুরে পাটা দিয়া চোদাই মু,1,sports
কুণ্ডার বাচ্চাকে আজীবন নিষিদ্ধ করা হোক।হালার পো কোন ভাল খেলা খেলতে পারেনি।মাঙ্গের পোরে বাদ দেওয়া হোক,1,sports
"আরে শালার পোলায় কয়কি,,,,হেয় নাক Celebrity,,,,ছাল নাই কুত্তার নাম রাখছে আবার বাঘা প্রতাব,,,,,,,শালা হিরন খোর,,,,,,।",1,sports
এমন চোদা দীসে এ্যাপীরে যা কখনো বিয়া করা দরকার নাই,1,sports
বার কাপ আনতে পারে নাই কোটি খেলাই ওপহার আর লাখ মাসিক বেতন তারপরে ও এতো দাবি আর এতো ডিমান্ড সালার প্লেয়ারদের লাঠি মেরে বাহির করে দাওয়া উচিৎ।,1,sports
এ খানকির পোলা কাপের,1,sports
তুই যে একটা শয়তানের বাচ্চা মাদার চোদ শালা হারাম খোরের বাচ্চা পাপন,1,sports
তুই আজহারী রে এখানে আইনা কি যে ভুল করছচ খানকির পোলা।।।।,1,sports
দুই বছর আগে কি হয়েছে আজ তার প্রাকাশ নাটক চোদায় বান্দির বাচ্চারা।,1,sports
বাইনচোত ফেক নিউজ ছাড়া আর কাজ নাইমাদার চোত,1,sports
সালার পুত রাজাকারের বাচ্চা ।,1,sports
রাজা কারের বাংলাদেশ ঐ শালা পাপ্পনইনডিয়ার দালাল এর বিচার কেকে চান,1,sports
"তোরা জাতীয় মাগী,তোরা ভোদা বিক্রি করো,পরে বেলাকমিল করো টাকার লোভে।",1,sports
সালারে লাথি দিয়ে বিসিবি থেকে বের করা দরকার।সালা ইন্ডিয়ার দালাল বাংলাদেশের ক্রিকেটের সবচেয়ে বড় কলংক এক সালায়,1,sports
জুতা মারি তার গালে পাপন তো একটা মাদার চোদ,1,sports
তুই শালা বক বক করস বেশি চুপ থাক হালার বাই,1,sports
বাচ্চা তুই তো করেছিস পাপন শুয়োরের বাচ্চা,1,sports
সব চামচাগো মায়রে চুদি😡😠😠,1,sports
বাল ও হবে না এই নাটা নাটা গুলারে নিয়া,1,sports
লুচ্চা হালাই চোখ দেখলেই বুঝাযাই,1,sports
নাছির কুকুরের বাচ্চাকে দল থেকে সারাজীবনের জন্য বাদ দিতে হবে,1,sports
ওই খানকির পোলা পাপনের বাচ্চা পাপন খানকির পোলা মাদারচোদজয়শ্রী করছো আর বিচার না কইরা আর যে চুরি করে নেওয়ার বিচার করবে রাইছ চোরের ঘরের চোর শালা কুত্তার বাচ্চা একদিন সামনে পাই তোরে মারমু তার জানিনা কি করবো,1,sports
জারসি পরা হিরোইন খোর শালা চিপায় নয়া মানিব্যাগ রাইখা দেয়নাই তো,1,sports
খেলাই পারে না দোনের বালারা আবার দর্শক এর ওপর রাগ খাটাই,1,sports
পাপন তর ভোলো হবে না মাগির ফুত,1,sports
চামচামি গুলো মাদার চুদ।,1,sports
দুর বাল ভালো করে কথায় বলতে পারস না,1,sports
হায়রে ছাগলের দলেরা। একটা নিরিহ ছেলেকে নিয়ে কি করবার লাগছে দেশটাতে চামচা ও চোরে ভরে গেছে। তাই এদের জোতা পিটা করা উচিত,1,sports
মাদারির বাচ্চা,1,sports
কুত্তার বাচ্চার কি ভাব,1,sports
মাদাচুদ পাপনে এখানে কেন খানকি পোলা কেউ বিছার মধ্যে টিপ দেইয়ার দরকার খানকি পোলা পাপন,1,sports
ও একটা পাগল চোদা বেয়াদব,1,sports
"রুবেল কে একদম ছাগলের বাচ্চা কালা দেবির মতো লাগে,,,, হাহাহা",1,sports
তর বউকেদে চুদতো মাদার চোদ তাছকিন,1,sports
ছোটলোকের সন্তান।,1,sports
পাগল না কি সব থেকে পাগল দেখছি তাসকিন,1,sports
বিদেশি মাগির পুত গো নামাইছোস কেন,1,sports
তোর মত মাদারসোথ থাকলে কেনিয়া হতে সময় লাগবে না,1,sports
বাইনচোদ সাকার লুচ্চা,1,sports
মাদার চুদ আনতাজে কথা কছ তরা,1,sports
একেক সালা রা ভুদা ভরে পায়তো তাই আর ভালো খেলাটা আসেনা। উলটা পালটা খেলে তখন। ফাউল টিম একটা।😡😠,1,sports
আরে চোদানির পোলারা টাকার চামচা,1,sports
হাইরে সোনা এদের কে কেন দিয়েছে সুন্দর সুন্দর সোনা গুলো হাজার হাজার মানুষে চুদে চুদে নষ্ট করে দিয়েছে হাই নষ্ট সোনা কি কর,1,sports
শালারপুতেরা বিবেকহীন উদীয়মান ক্রিকেটার মুশফিককে নির্বাচিত না করে বুঝালো যে তারা বোকাচোদা পুরো টুনামেন্ট জুড়ে মুশির ধারে কাছেও নেই রাসেল অথচ নির্বাচিত হলো রাসেল হাইস্যকর,1,sports
যারা বলেছে কুমিল্লা জিতবে নাহ ওরা সবাই খানকি মাগীর বাচ্চা এটাই প্রমাণ হলো 😂🤪 ওদেরকে কুত্তা দিয়ে চুদা উচিত😁😁 কুমিল্লা এবারো চ্যাম্পিয়ন হবেই হবে👌✌😊☺☺☺ কুমিল্লা ! 👌✌✌,1,sports
পাপন মাদার চুদ তুই কি তর মায়ের গোয়া দিয়া হইছিলে নাকি এই কানকির পোল মাদার ছোদ বেস্যার পোলা তর বাপেরে নিয়ে খেলা শুয়ারের বাচ্ছা আফ্রিকা জঙ্গলের হোনোমান,1,sports
"হ্যাপি বেশ্যা
",1,sports
পাপন ভাই সবাই আপনাকে গালি দিলেও আমি আপনাকে গালি দিবো নাহ। কারন হচ্ছে গিয়ে আপনি আমার খুব প্রিয় এক সেলিব্রিটি। আপনি এতো গালিগালাজ খাওয়ার পরে ও নিজের ইচ্ছায় অটল থেকে নিজেকে এক অনন্য উচ্চতায় নিয়ে গেছেন। সেটা সত্যি প্রশংসার যোগ্য। হেটার্সদের গালিগালাজ নিয়ে আপনি কোনো তোয়াক্কা করবেন নাহ। আপনি আপনার মতো কাজ চালিয়ে যান। দেখবেন একদিন আপনি দেশের সেরা বাইঞ্চোদে পরিনত হয়ে গেছেন।,1,sports
এই শালা কোন খেলোয়াড়ই না। বেয়াদব এক নাম্বার।,1,sports
আমি বাংলাদেশের সব মানুষকে আবেদন করতেছি বাংলাদেশের আপনারা কেউ খেলা দেখবেন না আমি বাংলাদেশের সব মানুষের হাতে পায়ে ধরি মাদারচুদ লীগপ্লিজ প্লিজপ্লিজপ্লিজপ্লিজপ্লিজবাংলাদেশের কে না বলুন।,1,sports
মুশফিকুর ভাই কিছু বলছে না আর চাম্চার বাচ্চারা কুত্তার বাচ্চারা কেউ কেউ করছে। ওই সাল্লা যখন বিশ্ব নবী সঃ গালি দেয় তখন কিছু হয় না এখন কি বলছে না ববছে এটা নিয়ে ফালাফালি,1,sports
দেশের ফুটবল থেকে দেশের মানুষ যেভাবে মুখ ফিরিয়ে নিয়েছে ক্রিকেটকেও কেউ চুদবে না।লিখে রাখেন কথাটা।,1,sports
সাকিব এর বুক টা ফেটে যাচ্ছে ।।।আহ্ রে সালা চুতিয়া পাপন,1,sports
মাশরাফি খানকির পোলায় কোথায়????,1,sports
দেশটা পাপনদের মতো মানুষ চুদে দিলো,1,sports
পান সালা,1,sports
মিডিয়ার মানুষেরা যা কিছু বলে সবকিছু সত্য না। মাঝে মাঝে মিডিয়ার মানুষেরা কিছু কিছু বানিয়ে বলে দেয় এবং আমরা সাধারণ মানুষেরা তাদের বানানো কথা সত্যি মনে করে থাকি। কিন্তু আমাদের এসব কথা বিশ্বাস করার দরকার নেই,1,sports
পাপন এর নুনু কাটা হক ।পাপন সালা নিজে একটা জুয়ারি,1,sports
বোকাচুদা,1,sports
পাপন মাদারচোদের পদত্যাগ চাই,1,sports
শালায় এই কারণেই খেলায় ডাব্বা মারে😡😠,1,sports
দুই বছর আগে কেন এই ঘটনাটা ফাঁস করল না ক্রিকেট বোর্ড এখন কেন তারা এই ঘটনাটা ফাঁস করল নিশ্চয়ই তাদের পাছায় ক্রিকেট খেলোয়াড়রা লাথি মেরে ছিল সেজন্য,1,sports
যেমন বোকা ছদা প্লেয়ার তেমনি বোকা ছদা দর্শক,1,sports
বঙ্গবন্ধুর নামে ক্যান খেলা হবে হালায়পারলে তোর নামে কর,1,sports
আপনি মুখে শূধু চাপাবাজি মানুষ ত্রক বোকা না,1,sports
পাপনদা একটা মাদারচোদ,1,sports
সালা দুইটাই মাগি আর মাগিবাজ,1,sports
ধন্যবাদ আপনাকে পাপনের মুখোশ খুলে দেওয়ার জন্য আপনি অনেক ভালভাবে কিলিয়ার করে দিয়েছেন পাপন কতটা মাদারচোদ,1,sports
ভাই কি বলবো বুঝতেচি নাঅার বলার ভাষা অামি হারিয়ে পেলেচিঅামি সাকিব ভাইর অনেক বড় প্যােন।এটায় এক মাত্র পাপন সরি ঘুষখোর পাপনের অনেক বড় অাবদান রয়েচে সে ইন্ডিয়ের দালাল মাগির হুতের পদত্যাগ চাই।অার সাকিব ভাইকে দলে চাই।কারণ সাকিব ভাই চারা বাংলাদেশ টিমের হ্যাড ভাঙা।সো পাপন হাটাও বাংলাদেশ ক্রিকেট বাঁচাও।,1,sports
তাসকিন পাগল,1,sports
"যাও মোহনলাল , বাংলা-বিহার-উরিষ্যার সাড়ে সাত কোটি প্রজা দিয়ে ঐ বার ভাতারি মাগীকে চুদাও । চুদিতে চুদিতে উঠিবে ফেনা, মুছিবার না থাকিবে তেনা ..মুহা হা হা হা হা হা হা ..",1,sports
আপনাদের মতো বোকা চোদাদদের জন্যই খেলোয়ার গুলো নষ্ট হচ্ছে।।।বার বার সমালচনা করে তাদের বারোটা বাজিয়ে দিয়েছে।।।। সে কি করবে না করবে সে তে আপনার কাছ থেকে শিখবে না।।।।মানুষ টাকা আয় করে নিজের খরচের জন্য।।।,1,sports
বুঝিনা মাল খেয়ে টাল হয়ে গেল নাকি 🍷শালা পাগল ছাগলে🐖ভইরা গেছে বাংলাদেশটা,1,sports
এই মাদার চোদেরে জুতা দিয়ে পিটাইয়া গাল ফাটাইয়া ফেল,1,sports
যারা যারা পাপোন্দাকে জুতা মারতে চান শুধু তারাই লাইক দিন,1,sports
পাপন কে জুতা মার।,1,sports
সাব্বির তোমার মারে চুইদা তোমারে এনেছি পৃথিবী তে মাগির পুত,1,sports
যুক্তি আছে বলে 😉😉😉,1,sports
পাপনের বাচ্চা বলে ফেল্ সব বিএনপি জামায়াতের ষড়যন্ত্র।,1,sports
সব চামচা সালা এমন করে দরে আছে মনে হয় সব কুত্তা,1,sports
মাগির বাচ্ছা পাপন্না,1,sports
শালা শুয়ার ভূয়া ভিডিও বানানো থেকে বিরত থাক।,1,sports
"বকাচুদা রুবেল তোকে দল থেকে বের করে দেওয়া উচিত
",1,sports
পাপন একটা মাদারচুদ,1,sports
ভাই আমার মনে হয় এই ঘটনায় পাপন শালা বাটপাররে নাটের গুরু বানিয়ে বুভো হাসিনা এই কাজটা করতেছে কারণ সাকিব দলে থাকলে ইন্ডিয়ার থেকে ভালো খেলতো বাংলাদেশ কিন্তু বোবো তা চাইনা।,1,sports
তোর মারে চুদু মাগির পুলা,1,sports
এই শালা পাপন তুই পদত্যাগ কর যদি লজ্জা শরম থাকে।,1,sports
এই সালা আবুল,1,sports
এর মারে আর এর বেনেরে সবাই মিলি চোদেন জাতে এই মাগির পোলা ভাল ভাল নিউচ করে খান কি মাগির পোলা ভাল হয়ে জা,1,sports
চোদ পাপন,1,sports
তোমরা সব মারচুদ,1,sports
তুই চোর সালা পাপন,1,sports
সাকিব ভাই।কি কোন জেলখানের আসামি নাকি এই ভাবে ছবি তুলতে হয় সালার সাংবাদিক,1,sports
সাকিব কে বছরের জন্য নিষিদ্ধ করেছে আইসিসি। দ্বায় স্বীকার করার বছরের শাস্তি স্থগিত। খেলায় ফিরবে সালের অক্টোবর। সাকিবের এই শাস্তির জন্য সাকিবের চেয়ে বোর্ড বেশি দ্বায়ী। ফিক্সিং এর তদন্ত করতে বছর সময় লাগার কথা নয়। হটাৎ করে এতো দিন পর কেন এই শাস্তি আসলো!! কিছু দিন আগে পাপন হুংকার ছেড়ে বলেছিলো আপনারা শীঘ্রই ফিক্সিং এর খবর পাবেন। আইসিসির আগে ঐ কুলাঙ্গার কিভাবে জানতো ফিক্সিং এর শাস্তির বেপার। বোর্ডের যে কর্মকর্তাই হোক আইসিসি কে সাকিবের এই খবর দেবার পর ই আইসিসি তাদের আইনিপদক্ষেপ নিয়েছে। কল ট্রেকিং করা হয়েছে তাছাড়া কেন বছর পর!! মূলত পাপন ই এই কাজ করেছে। সাকিব হয়তো বুঝতে পেরেছিলো যে সে শাস্তি পাবে তাই বোর্ডের চুক্তি লংঘন করেই গ্রামীণ ফোনের সাথে চুক্তি করেছে। বুদ্ধি আছে বলতে হবে। সাকিবের উচিত বাংলাদেশ ক্রিকেট কে বিদায় বলে দেওয়া। এবং অন্য দেশের হয়ে ক্রিকেট খেলা। তারপর এরা বুঝবে কি মূল্যবান সম্পদ হারালো। (এটা আমার ব্যক্তিগত মতামত),1,sports
পাপনের মায়েরে চু সালা কুত্তার বাচ্চা,1,sports
সাকিব এটা পড়ো টা পাপন চাল আমরা বুঝতে পারি শালা কত বড় কিমিনাল,1,sports
মাদার চুদ মিডিয়া,1,sports
পাপনকে ডিম থ্যারাপি দিতে হবে শালায় করম চোদ,1,sports
মুশফিকুর ভাই একটা পুংটা মোটা রে দিয়া বল করাই🤣,1,sports
কিছু জারজ আনলাইক দিচ্ছে,1,sports
পাপনের গালে জুতা মার তালে তালে,1,sports
এই জারছি পরা লোকটাকে জুতা পিটা করার দরকার এখানে একটাও ইমান আলা লোক নাই ছেলে টাকে কেন এত অপমান করা হলো ছি ছি এখানে সবাই চোরের বাচ্চা চোর,1,sports
তোর মারে চুদি নটির পোলা রেন্ডিয়ান তোর চ্যানেল পারলে বাঁচা। ভুয়া ভিডিও দেস কর তোর চ্যানেল এ সাসপেন্ড হবে পারলে ফিরিয়ে আনিস।,1,sports
মাদারচোদ পাপন যুতে মার,1,sports
পাপন তোই থাকা লাগবে না কুতথার বাচ্চা।,1,sports
পাপন খানকির পোলার বাবা জিল্লুর রহমান তো ভালো লোক ছিল এই মাগির পুত পাপনবাজার পদত্যাগ চাই 👇👇👎,1,sports
আরে পাপন শুওর এর বাচ্চা টাকা খায়ে যাচ্ছেআর এই ভারত সফর পুরোটাই ফিক্সিং😒 মাদারচোদ পাপন টাকা খায়ে যাচ্চে জানোয়ার এর বাচ্চাওর মাথাটা কেউ পদ্দা সেতু তে পিলার এ ঢুকায় দে কেউ ভাই।,1,sports
এরা জাতীয় জানোয়ার ।,1,sports
পাপন খানকির পুলা তুই বারে বার সক্ট হচ্ছিস কেনো । তকে যখন সাকিব বেপার টা যানিয়েছে তখন তুই তাকে চেপে যেতে বলছিস কেনো ওই ভারত এর জুয়ারি দের সাথে কি তর হাত আছে ।,1,sports
মাদার চুদ আরো আগায়া নিবো দেকবো কেমন আগায়া নেই,1,sports
কানকির পুলারা ওরা,1,sports
ফুটপাতের টোকাইগুলা যখন টাকাকড়ি আর সম্মান পায়। lol,1,sports
পাপন গং দের পাছায় লাতি মেরে বাহির করে দেওয়া হোক।,1,sports
শালা জাউরাতুই যে মাসে লাখ টাকা বেতন পাসওটা কি,1,sports
খারাপ কি আমাদের দেশর অনেক খেলোয়া ১০ বছর খেলে ও একটি ১০০করতে পারেনি ১৮ বছর খেলে ও পারেনি,1,sports
চুতিয়া পাপনের পদত্যাগ চাই,1,sports
তাসকিনের মতো বলার কে বাদ দেওয়ায় আজ বাংলাদেশ টিমের এই অবস্থা সব ম্যাচ হারতাছে সালারা।,1,sports
পাপন এর পদতেগ চাই। বাইনচোদ পাপন।। তোর কথা সুনলে গা জ্বলে মন চায় তোরে কম হলেও মিনিট গালি দেই।।,1,sports
পাপন হালা চিন্তায়কালো হয়ে গেছে।🤣🤣🤣,1,sports
কোন বাল খেলেতাদের এক কোটি টাকা দিবে,1,sports
"এ কুত্তারবাচ্চা, রুবেল গান গাইলো কখন??",1,sports
সাংবাদিক ভাই সাকিবের ডান পাসের কুততা পাপোনের ছোবি কেনো তুলছো,1,sports
হালায় পুরা গাজা খোর,1,sports
পাপন তোর বিচার আল্লাহ করবে শালা তুই যা করলিআর বাংলাদেশ ক্রিকেট কে ধ্বংস করে দিলি,1,sports
শখ তোর বউয়ের ভোদায় দে।।ফুটবল কে শেষ করছে এখন ক্রিকেট টা ধংসের দিকে নিয়ে যাইতেছে শুয়েরের বাচ্চারা ।।আর ভারতের সাতে তুই খেলিস আর তোর পরিবার দেখবে।।সোনার বাংলাদেশ আর কিছুই রইলো না ।। এ দেশে বসবাস করা আর জিন্দা মরা এক কথা।,1,sports
পাপন খানকির পোলা।তোর আওয়ামী লীগের গুষ্টি চুদি। তোরেও চুদি।মাদারচোদ খানকির পোলা।,1,sports
বাংগালি যে কি খারাপ মানুষের পাছাই বাশ দিতে পারলেই বাচে।,1,sports
বাঙ্গালী একক ভাবে কাপুরুষ দলবদ্ধভাবে জানোয়ার।এ ভিডিও দেখলে সেটা বোঝা যায়।সামন্য একটা বিষয় নিয়ে এতো হয়রানি।,1,sports
খানকির পোলারা পুরো টুনামেন্টে ভালো বল করেছে মোস্তাফিজ এবং ভালো ব্যাটিং করেছে মুশফিক সেরা হয় রাসেল মদ খা মানুষ হয়,1,sports
এটা পাপনের কাজ মাগির পোলারে কুত্তা দিয়ে চুদানো,1,sports
এই ঠাপোইন্নারে লাথি মেরে বাহির কইরা দিলে সব ঠিক হয়ে যাবে । শালা দুর্নীতিবাজ এরে দুর্নীতি দমন কমিশন ধরে না কেন,1,sports
মুশফিক চাটের বাল একটি মানুষ কি সবার কাছে সমান মত ভেদ থাকতেই পারে,1,sports
দালালল মাগির পোয়াপাপন্নের মারে চুদভাই তুই খেলা ছাড়ি দে খেলার মারে চুদতুমার কাছে কি টাকার অভাব আছেব্যবসা কর যাপাপন্নে আর পাপন্নের বউ খেলক।,1,sports
থালা নিয়ে ফুটপাতে দাড়ায়ে দাও।,1,sports
পাপন মাদার সুদ,1,sports
নাজমুল ইসলাম মাদার চুদের বাচ্চারে যতদিন লইবো ততদিন ঠকবে,1,sports
শালা তুই আবালকিছুই জানিস না তুইএই কাজের শাস্তি সর্বনিম্ন মাস আর সর্বোচ্চ বছর আজীবন না আবাল মাদারচোদ জানিস না কিছুই আবার ভিডিও বানাসমাদারচুদের বাচ্চা তুই একাই জানস আর তো কেউ জানে নাশালা বাইনচোদ এতো দিন পরে আসছস বলতে মনে হয় আর কেউ জানে নাখানকিরপোলা তুই আসলেই মানুষ হবি না,1,sports
তর মায়েরে সালা চোর তর মাইরে সালা চোর চোর চোর চোর চোর চোর চোর চোর চোর চোর চোর চোর চোর চোর চোর চোর চোর চোর চোর চোর চোর চোর,1,sports
সারা বাংলাদেশের মানুষ মিলেপাপনের গালে জুতা মারা উচিৎ,1,sports
আওয়ামী লীগের সালারা সব পারে এটাই প্রমান,1,sports
বোকা চোদারা মারামারি ভিডিও করো,1,sports
তুই একটা মাদারছুদ,1,sports
তোমার গুয়ায় গরম ডুকানো উচিত শালা মিথ্যুকের বাচ্চা,1,sports
যাকে গালি দেয় সে কিছু বললোনা আর মাদাচুদেরা চামচামি দেখ সব কয়টা মনে হয় দালাল আর জারিস পরা সালার পু মনে হয় বাবা কুর সালা চামচামির বাচ্চা সব,1,sports
পাপনের মায়রে বাপশালারে একেবারেই দেখতে ইচ্ছে করে না,1,sports
এই শালারে চোরের মত লাগে বালবির,1,sports
যে লোকটা বাংলাদেশের জারসি পরে পিছনে হাত ধরছে ওরে জুতা দিয়ে পেটানো দরকার।,1,sports
মুসফিক আমার বাল চুদানির পোলারা ছাড়।,1,sports
আজ আমি খুব খুশি সাকিব কুত্তা ব্যান হয়েছে।। শালা,1,sports
শালা পাপন পাগলা চুদা,1,sports
দর্শক একটা না পাঁচটা বলতেই পারে তবে এই ছেলেকে এত কিছু করা ঠিক হয় নাই মূলত দুষ্ট হয়েছে ওই বাংলাদেশের জার্সি পরা গাঁজাখোরের বাচ্চাটার একটা মাগির পোলা নাইতে সামান্য দু চারটা কথা বার্তার জন্য ছেলেটি তার মান ইজ্জত হারালো আর ওই গাজাখোরের বাচ্চা ওর মায়ের কসম বলছে শুনিস নাই,1,sports
তর বগবানের ধনটা কাইট্টে তর মার সোনাদে ডুকাইয়া দিমু,1,sports
পাপনের গুষ্টিরে চুদি,1,sports
মাদারির বাচ্চারা আমার বালের হাইলাইট করে।হাইলাইট ও টেনে টেনে দেখতে হচ্ছে।,1,sports
দুনিয়াতে এতো মানুষ মরে শালার আওয়া লীগের কুওায় মরেনা।,1,sports
ছবি তোলা আর সঙ্গ দিলেই কি খারাপ হয়ে যায় মানুষ ? এই জন্নই তো আমারা আজ এতো পিছিয়ে আছি আর সবারই নিজেসশ জীবন আছে তার মত করে তাকে চলতে দিন,1,sports
আলা হিজরা,1,sports
তুই সবার মারা যাওয়ার কথা বলিশ তুই কখন মারা জাবি শালা,1,sports
"পালতু মাদারচোদ,,, রুবেলকে নিয়ে মিথ্যাচার হচ্চে",1,sports
মাগির পোত কে জুতা দিয়েপিটাও,1,sports
সব খানকির পুত,1,sports
এমন একটা ভাব শালাদের মনে হয় কি না কি হইয়া গেছে আর বিশ্বের এক নাম্বার টিম হইলে অগো পা ও পড়ব না জমিনে খেলোয়াড় এর উচিত টেম্পার ঠিক রাখা দর্শক এর কাজই আজাইরা সমালোচনা করা তাই বলে কি এভাবে ব্যবহার করবে,1,sports
গালি দিয়েছে তো কি হয়েছে কুত্তার বাচ্চাদের এত গায়ে লাগছে কেন,1,sports
সাথে ওই গাজাখুরটা কে সালা নীরহ একটা ছেলেকে একা পেয়ে কী ভাবটা মারলো।,1,sports
সালার‌ বেটারা‌ টাকার জন্য খেলে দেশের ‌জন্য না,1,sports
হ্যা রে কুত্তার বাচ্ছা কোন টি ভি নিউজে আসে নাই কেন ?,1,sports
পাপনের পদত্যাগ চাই।।।ওই ম্যাদারচোদের পদত্যাগ চাই।।।।,1,sports
বাংলাদেশ যেরকম বাংলাদেশের নেতৃত্ব সেরকম দেশের প্রতি ঘৃণা নাই। দেশের হারামখোর মানুষদের প্রতি ঘৃণা। বাংলাদেশ ক্রিকেট বোর্ড বাংলাদেশের কোন বাল ফালাইছে। এইটা দেশের যা উপকার না করছে তার চেয়ে বরং ক্ষতি বেশি করছে। ফাডা মারখা মিডিয়া আবার এই সমস্ত জিনিসের পাগল। কতো মারাত্মক জিনিস ঘ‌ইটা যাইতেছে দেশের ভিতরে এগুলার খবর নাই। রামছাগলের দল একটা কিক্রেটারের কোয়ালিফিকেশন কি কোন জায়গার সম্মান কোন জায়গায় দিলিরে বেকুবের দল।,1,sports
"কমপানির মাছ বেশি পানিতে পড়লে যা হয়।হুটেল বয় হয়ে এখন ইসটার হয়েগেছে তার কি আর হুসবুদদি টিক আছে।তার কি লজজা সরম আছে থাকলে কি এই অনইতিক কাজ অনলাইনে করত,তার মা বাবা ভাই বুন গুরুজন সবাইকে দেখাইয়া কুকরম,করচে বংসদার পুলা হলে এইসব করতনা।",1,sports
ঔ খানকির পোলারা কই গান কয়,1,sports
ভাই আপনার ভিডিওটি শুনে অনেক খারাপ লাগছে মন চাইছে পাপন কুত্তার বাচ্ছাকে জুতা পিঠা করি।এটা এই কুত্তার বাচ্ছার চক্রান্ত।,1,sports
কে কোন বাল দেখতে নেয় বুঝিনা আর সে লাষ্ট কবে একটা ফিফটি করছে কেউ বলতে পারবে?? আবালদের দলে সুযোগ এখনো দেয় ভাবতেও অবাক লাগে,1,sports
পাপন চুরা হালা এটা কি করলি,1,sports
জার্সি গায়ে বাইনচুড ডা তো গান্জাখোর,1,sports
সালা তুই পদত্যাগ কর,1,sports
আর যাইহোক পাপনের কতাবার্তা খুবই খারাপ এবং রুড়।আজ ওদের জন্যই আপনার মতো বালকে সবাই চেনে।,1,sports
সালা তাসকিন মাদার চুদ গবির সেলেটা কে নিয়া,1,sports
"এরকম বেয়াদব খেলোয়াড় চাই না,,, সাব্বির একটা মাগি বাজ,,,শালা একটা বেত্তমিজ খারাপ ছেলে",1,sports
পাপনকে জুতা মারতে কেউ চান কি এই মাগির পুতের কারনে আশ দেশের খতি হলো সবার সামনে,1,sports
তোর মারে চুদিতে চুদিতে মরে গেলো তাই না মাগির বাচ্চা,1,sports
তুইতো একটা বাইচোদ,1,sports
পাপনের বিচি লক,1,sports
পাপনের দুই গালে জুতা মারো তালে তালে👞👞👞👞,1,sports
পাপন একটা পাগল 👿👿,1,sports
পাপন ছাগলডার পাছায় লাথি মেরে বিসিবি থেকে বের করা হোকক্রিকেটারদের বাশ মারছে গত বছর ধরে,1,sports
মুশফিক কোন ধোনের বাল অামার ওই মাদারচোদ কে গালি দিছে তো কি হইছে ফেসবুক লাইভে হযরত মুহাম্মাদ সাঃ কে গালি দেয় তখন কিছু বলে না অার মুশফিক কোন ধোনের বাল তাকে কি না কি গালি দিছে নিশিদ্ধ পল্লিতে জন্ম নেয়া কুত্তার বাচ্চাদের গায়ে অাগুন ধরছে,1,sports
মাদারিরবাচ্চা পাপনই এই কাজ করছে,1,sports
জনগন কোটি কোটি টাকা তাদের পিছে খরচ করে আর একটা গালি দেওয়াতে কুত্তার মত গেও গেও সুরু করছে কেন কুত্তারবাচ্চারা,1,sports
তাসকিন একটা বলদ___ কাজটি ঠিক করে নাই,1,sports
এই পাপন কুত্তার বাচ্চা সাকিবকে প্রতিশোধ নিলো হরতালের এই বদমাইস তুই জানিস না যে তোর এই পাওয়ার কয়দিন থাকবে ? কিন্তু সাকিব সবসময় থাকবে,1,sports
পাপন একটা মাদারছুদ।।। কুত্তার বাচ্ছা তর গোস্টি তে সাকিবের মতো একটা প্লেয়ার বের করে দেখাতো।।।।।।। তুই কি জানিস কুত্তার বাচ্চা একটা প্লেয়ার নিজেকে সেট করতে কতোটা পরিশ্রম করতে হয়।।।,1,sports
সকল দোষের কারণ পাপন ওই শালারপুতে ঘটাইছে সব,1,sports
ধন্যবাদ তাহমিদ ভাইয়া,1,sports
দেব কি স্বাভাবিক ভাবে কথা বলে রিপোর্ট করতে পারে না? এইটা কি স্টাইলে কথা। ভাষার ধর্ষণ।বালের বিশেষজ্ঞ,1,sports
হায়রে নিয়তি সব শূয়ের বাচ্চা,1,sports
পাপান তো কুত্তার বাচ্চা,1,sports
তরে ঘোড়া দিয়ে চোদানো দরকার,1,sports
প্রত্যাখান তো করেছে না কি এই শুয়োরের বাচ্চারা আইসিসি ঘুস তো খায়নি?? আর জানায় নি তো কি বাল হয়েছে তোরা কার বাল রে?? জানালেও বা কি বালটা ছিঁড়বে তারা কি জানেনা কে কে বেটিং করে জুয়া খেলে?? এরপরও কিছু করতে পারবে না পরিষ্কার কথা কারণ ওরা তাদের বাপেরও বাপ। সাকিব ভাই তোমাকে স্যালুট ঘুস না খাওয়ার জন্য। আচ্ছা টা কথা বলি এখন তো আইসিসির খানকীরা জানতে পেরেছে যে কে বা কারা সাকিব ভাইকে ফোন করে প্রস্তাব দিয়েছিলো তো এখন কি বালটা ছিঁড়বে মশাই অথবা কি বালটাই বা ছিঁড়তে পেরেছে ঐ জুয়ারীদের?? মাগীর বাচ্ছারা শুধু পারবে যে ঘুস খায় নি তাকে পুরস্কৃত না করে তাকে না করে উল্টো সাজা দিতে। এই বাইনচুদের বাচ্ছারা আইসিসি তোদের আবার কিসের বালের এন্টি করাপসন ভুরো রে?? ঐটা দিয়ে কি একে অপরের বাল ছেঁড়া ছেঁড়ি করিস?? কুত্তার বাচ্চারা। নিরপরাধ মানুষটিকে সাজা শুনিয়ে নিজেরা খুব এইটা চোদাও না?? আর যারা জুয়া খেলে তাঁদের পা চাটো কমিশনের জন্যকুকুর চোদারা। বাংলাদেশের ক্রিকেট বোর্ড আরও বড়ো বাইনচুদ। শুধু পোষ্ট চায় টাকা চায় কিন্ত পাশে দাঁড়ায় না প্রতিবাদও করেনা। দুর তোরা মর শালারা। বাংলার ক্রিকেট বোর্ড আর সিনেমা বোর্ড একই পয়সার দুটো দিক একিজাত। আর বললাম না।সাকিব ভাই জিন্দাবাদলাভ ইউ 😘,1,sports
খেলোয়াড় সব জামাত শিবির হয়ে গেছে ।সবগুলোরে ক্রস ফায়ারে দিয়ে দেন।সমাধান এর জন্য কি পদক্ষেপ নিচ্ছেন সেটা নিয়ে কথা না বলে এখানেও বালের নোংরা পলিটিশিয়ানের মত কথা বলেন কেন।এখানেই আপনার সভাপতি হিসেবে যোগ্যতা সবার বুঝা হয়ে গেছে ।,1,sports
"বাংলাদেশ ক্রিকেট টিম পুরোই লুচ্চা তে ভরে গেছে। প্রায় সব কটা প্লেয়ার অবৈধ সম্পর্কের খবর পাওয়া যায়, ক্রিকেট খেলা হলে আগে ধনী আর বাকিদের মাথা কাটা ছবি দেখা তো এখন ভারতের টেনিস প্লেয়ারের সাথে অসভ্য আচরণ করে। এরা মানুষ না কি মানুষরূপী জানোয়ার কে জানে। ভাগাড় থেকে উঠে আসা মানুষজনের থেকে এর থেকে বেশি কি আশা করেন.......",1,sports
মুশফিক কোন চেটের বাল,1,sports
সব কয়টা হারামির বাচ্চা,1,sports
পাপান মাদার চোদ,1,sports
পাপন মুখে জাই বলুক মনে মনে অনেক খুশি।গাছের ঘুরা কেটে উপরে পানি ডালছে পাপন কুত্তার বাচ্চা,1,sports
শালা খেলোয়ার না হলে তোরে পাগলীও বিয়ে করে চুদতোনা,1,sports
পাপনকে কুত্তা দিয়ে চুদাই,1,sports
পাপন তুই হারামি এই কাজ করেছিস,1,sports
দূর কুকুরের বাচ্চা,1,sports
আপনি একদম সঠিক কথা বলেছেন ভাই। পাপন শুয়রের বাচ্চাকে পাইলে জুতাপিটা করতাম। শালা হারামির বাচ্চা জুয়াখোর।তারে বহিস্কার করা প্রয়োজন।,1,sports
পাপন মাদাচোদ কে আল্লাহর কসম পাসে পেলে জোতা দিয়ে পিটাতাম😡😡,1,sports
পুটকি দিয়ে ওর গরম ডিম ঢুকানো হোক,1,sports
ভাই পাপনের পাছায় লাতি মার সবাই,1,sports
টাকা কি তোর বাপের পকেট থেকে দিছএত ভাব চুদায় কথা বলিস,1,sports
কুমিল্লার বোলিং বালের,1,sports
পাপন খানকির পোলায় এর জন্য দায়ী খানকির পোলারে বিসিবি থেকে বহিষ্কার করা হোক।,1,sports
বালের এক কথা বার বার ভাল লাগে না। গুরু টিক কাজ করছে। আবার করবে। করো সমস্য।,1,sports
সিলেটের মান ইজ্জত সব ডুবাইছে আচোদা দল গঠন করে।,1,sports
নটির বাচ্চা পাপন সব কিছু করলোমাদার চোদ তুই পদ থেকে সরে যা,1,sports
তোদের কোটি মানুষের কপালে হিছা মারি শালার পুতেরা কুত্তার বাচ্চারা তোদের সমস্ত বাঙালি জাতিকে বলতেছি তোদের কারণে আজ দেশের এই অবস্থা শালার পুতেরা গরিব ভাত চিকিৎসা পাচ্ছেনা আর শালা রা লুচ্চামি করার লুচ্চামি করার সুযোগ করে দেয়,1,sports
পাপন সালাগো জন্য আওমলিগো বদলাম,1,sports
ভদা কও না খানকির পলারা তুই শুধু ভিও বারানর জন্য,1,sports
আমার মনে হয় সাকিব আল হাসান ঘুষ না নেওয়ায় পাপনের অনেক বড় লস হয়েছে🙄 তাই পাপন এই কাজ করেছে 😊😊😊 শালা ঘুষখোর পাপন 🤪🤪,1,sports
ধিক্কার জানাই পাপন সালা কুত্তার বাচ্চা কে,1,sports
পাপননান্নুসুজন সব শালা হারামি,1,sports
মুশফিক একটা বাল,1,sports
তোমরা এগুলোই পারবে। মাঠে বাল তুইলা হাঁটা দাও।,1,sports
শালারা খেলা পারেনাআবার শালারা ভেতন ভাড়ানোর খেলা বন্ধ করেশালাগোরে জুতা মার।,1,sports
কোন যোগ্যতায় রবি কুমিল্লার দলে খেলে। তাও আবার ওপেনিং। আজকে কুমিল্লা হারার মূল কারণ রবি আর সাব্বির। এদের ধীর ব্যাটিং এর কারণে কুমিল্লা হারছে। কোন মাদারচুদে এদেরকে দলে নেয়।,1,sports
তোর ভিডিওর মারে চুদি খানকির বাচ্চা গুজব খোরসমাজটা তোদের জন্য শেষ হয়ে যাবে হাহাহা যারনেওয়ালা চোদায়ছে গুদের বিটা,1,sports
রুবেলের চেয়ে ভাল ভাল খেলুয়ার আছে দেশে গাজা খুর কি ভাবে খেলতে পারে,1,sports
সালা ডান্ডি র বাচ্চা তোর বাবা মরছে নিউজ দে।,1,sports
শালার গরের শালা তুর বংষের বিতরে আর পাগল আচেনে,1,sports
তুমি পাপন বালের চেয়ারম্যান হয়েছে?? প্লেয়ারের খোঁজ খবর রাখো না কার কি হয় না হয়?? পদত্যাগ কর শালা,1,sports
আপোন্দা কে বছর পোন্দে বাশ ডুকাতে হবে,1,sports
খালি প্রধানমন্ত্রী প্রধানমন্ত্রী করে কেনসালা চোরতেল মাইরা চলে,1,sports
তুমি চুদা দিছ মজা পাইছ আর কি,1,sports
হোলের খেলা দেখবো আর।বাংলাদেশ ক্রিকেটের মাইরে চুদি।পাপনের মাইরে চুদি।,1,sports
কুমিল্লার কিপার একটা আবাল,1,sports
তুর হেডা,1,sports
আপনারা ওনার সাথে এরকম করেন কেন শালার চামছারা,1,sports
পাপন কে মাএ পাচ রীমেনটে নেয়া হক সব বেরীয়ে আসবে সালা বাংলাদেশের এক নাম্বার চোর,1,sports
প্রিয় পাপন!! যে যাই বলুক না কেন আপনার মতো সৎদেশপ্রেমিক আর দ্বিতীয় টা হয়না আপনি বাংলাদেশ ক্রিকেটের যে পরিমাণ সাফল্য এনে দিয়েছেন তার জন্য পুরো বাংলাদেশ আপনার কাছে কৃতজ্ঞ থাকবে। তুমি যদি এসব ভেবে থাকো তাহলে তুমি সালা আসলেই একটা বাইঞ্চোদ,1,sports
পাপন কে জুতা দেয়া হক,1,sports
পাপনের মারে বোনরে মেয়েরে চুদলে সালা পদত্যাগ করবে,1,sports
এই পাপন সাকিব খেলবে না তোর বাবাকে নিয়েজা।শালা শুয়ারের বাচ্ছা।,1,sports
এইটা পাপনের কেলেংকারি এই সালাকে সবাই মিলে পিটাতে হবে তাইলে সে এখান থেকে সরবে,1,sports
আজকে সংবাদ। এই নিউজ দিচ্ছে হাতের মাকে চুদা দিচ্ছে,1,sports
মাদারচোদ। তুই। যে জুয়াখেলার। দরা খাইছোস। তোর। বিচার। হবো না আবার। ইংল্যাডে ই যে জুয়াতে দরা খাইলো ওর। তো বিচার। হলো মাদারচোদ।,1,sports
মাগিরপুলা,1,sports
খানকি পুলা তুই মৃত্তুর খব র ভুয়া দিস তুই সালা নাস্তিক। ।। । কি,1,sports
নাছিৱ ইবলিশ,1,sports
খানকির পোলা পাপন এখন আবেগ দেখাইতাছে,1,sports
পাপন কুওার বাচ্চা এই শালা সয়তান কুওা সবকিছুই নষ্ট করছে শালা পাপন হারাম কুরের বাচ্চা পাপনতু দেই শালা তা বাপের টাকা য়ে কাউকে দিতে হবে,1,sports
আরে মুশফিক মাদার চোদ,1,sports
তগো গালি না দিয়ে জুতা মারা দরকার ছিলো জানুয়ারের বাচচারা এই পাবলিকের জন্যে তুরা খেলুয়ার তুরা হলি অমানুষের বাচ্চা,1,sports
ফুটবলে উন্নয়ন দরকার।ক্রিকেট বাদ দেন।ক্রিকেট অনেক লাইক করতাম।সালারপুতদের নাটকে আর ভালো লাগের না।,1,sports
পাপন কে জুতা পিটা করে পদ থেকে নামানো হোক,1,sports
সব বলদ,1,sports
আরে তাসকিন বাদ গেলো কেন দুইটা থাপ্পড় তাসকিন কেউ মারা উচিত ছিল তাহলে ওর হাসি হোগা দিয়ে বের হতো দুইটা গাধা কে রেস খেলাইতেছে একটা গরু,1,sports
মুশফিক কোন চ্যাটের বাল পাবলিক গালি দিবে জুতা মারবে এতে কি সমস্যা,1,sports
শালা পাপনকে হাতের কাছে পেলে কি যে করবো নিজেও জানিনা। আজ থেকে বাংলাদেশের খেলা দেখা বাদ দিলাম।।,1,sports
কুত্তার বাচ্চা এত খারাপ ওয়াক থু খানকির বাচ্চার মুখে👎,1,sports
মাদার চোদ পাপন সালা তোর পদোতেক চাই,1,sports
সালা গাজা খাইয়া মর,1,sports
তুমি আমার বালডা বোঝ।সাকিবের নিষিদ্ধ হবার প্রক্রিয়া বহুত আগেই শুরু হয়েছিল।,1,sports
পাপন চুতিয়ার মুখে থু থু মারতেও ঘেন্না হচ্ছে 😡,1,sports
এটা কোনো মজা হল সালা আমরা বুযিনা,1,sports
তুই সালা মিথ্যা কথা বলছ পাপন তুই করেছিল এটা,1,sports
মাগির পোলার পিছন দিয়ে গরম রড দে,1,sports
হায়রে পাপন এই ভাবে প্রতিশোধ নিলিদেশটার হোগা মাইরা দিলি।,1,sports
আই সিসি আর পাপনের গুষ্টি চুদি,1,sports
তোদের মতো পাগল ছাগলের কারনে আজ দেশের মানুষের এই অবস্থা তোরা দেশে গুজব ছড়িয়ে দিছশালা কুওার বাচ্চারা।।,1,sports
খানকির পোলা তুই পদত্যাগ কর,1,sports
প্রতি দিন অলি গলিতে হাজারো পাপনের জন্ম হয় হবে। কিন্তু হাজার বছরে একজন সাকিব পাওয়া যায় না। অবিলম্বে পাপঅন কুত্তার বাচ্চার পদত্যাগ দাবী করছি।,1,sports
কুমিল্লায় দেশি কয়টা বলদ খেলে তারা কুমিল্লাকে ডুবাইছে।,1,sports
গালী দিছে তো কি হইছে আমি দিলাম কি বাল ছিরবো আইতে বলিস হোগা দিয়া বেট ডুকাইয়া দিমু কতো গালী দিছে পাবলীক জিবনে কোনোদিন গ্যালারীতে ওঠে না।।এরেই বলে ছল নাই কুত্তার বাঘা নাম।।😡😡,1,sports
"আমি খেলা দেখি যত দিম ধরে একদিন দেখলাম না সাব্বির ৫০-রান করতে,,সালা কোনো কাজের না।",1,sports
আপনারা চামচারা একটু বেশি করতাছেন সে আল্লাহর কছম কাটছে এবং মায়ের দুধের কচম কাটতাছে তারপরও আপনারা জেরা করতাছেন চামচামি একটু বেশি হয়ে গেল।,1,sports
সালা মাদার ছুদ,1,sports
কত বার চোদা চুদি হযেছেরে তোদের মধ্যে লুচ্ছা ছেরি ছেরা,1,sports
বাটপার বাইনচোদ কোথায় রুবেলের গান,1,sports
বালের ভিডিও ছারচে হালারা,1,sports
না খেললে নাই শালারালোভ বেড়ে গেছে জনরে কোটি টাকা? ওরে বাপরে এটার তিন ভাগের একভাগ ফুটবলে কাজে লাগাইলে অনেক উন্নতি হইতো ফুটবলের৷,1,sports
খানকির পুত মালাউন তর বুন কে গাইর মারি মালাউন তুরা আর কি হবি কুকুর ও চুদে তর বুনকে আর গরু চুদে তর মা কে আর মহিশ চুদে তর বাবা কে কুকুর চুদে তকে মালাউন সুওরের বাচ্চা এই রকম মিত্যা নিউজ কেন দেস মালাউন,1,sports
এরই নাম বাংঙ্গালী কত্তো ছুট লোক হলে একটা কথার কারনে তার শাতে এই রকম ভেবহার তরা কি মানুষের জন্মের কাত্তার বাচ্চারা শে তার মা আল্লাহ্ কছম করতেছে তার সাতে কি ভেবহারটা না করলো এই মাদারচোদেরা,1,sports
মুশফিক আমার শাউয়ার বাল হালারা আমার শাউয়া খেলে কোন বালডা পালাইছে দেশের জন্য ক্রিকেট খেলে আবার ভাব চোদায়,1,sports
"মাদারচুদ রুবেল তরে কুত্তার মত পিটাবো
",1,sports
তুই তো তোর বাপের পাছা দিয়ে বাইর হইছোস,1,sports
পাপনের পদত্যাগ চাই।দূর্নীতিবাজ হালা।,1,sports
তোম মারে হোদাইচে সালার পুত,1,sports
সাব্বির সালা একটা মাঘীবাজ লুচ্চু,1,sports
তুগো দালালের মাইরে চুদি,1,sports
আমি বলি কারো দোষ না দোষ এই প্লেয়ার্ মাদারচোদেগো ।মাদারচোদেরা খেলতে পারেনা আরেকজনের দোষ দিয়ে লাভ নাই,1,sports
পাপন হালাই সেস করছে ক্রিকেট টিমকেনিজের চিন্তাতে খেলোয়াড়দের বাঁশ দিয়ে যায়তাছে পাপন হ্লায়,1,sports
পাপোন একটা মাদার চোদ,1,sports
কিরে শালারপুত তুই কী তোর বাপের পুটকী দিয়ে হোইচোছ বাইনচোদ এখন যে সবাই তোর মায়রে খারাপ বকা দেয় তোর ভালো লাগে।,1,sports
মদ খা চোদানির পুত মদ না খাইলে তুই মানুষ হবি না,1,sports
তোর বোনের কাছে খানকি মাগূর পুলা,1,sports
মাদারচোদ পাপন তুই সাকিবের পাশে কেমনে দাড়াস তোর যোগ্যতা আছে সালা বাটপার। বাংলাদেশের খেলাই আর দেখমু না,1,sports
শালা শুয়েরের বাচছারে জেতা পুরা উচিত,1,sports
পাপননান্নুসুজন এই তিন হারামজাদাকে সবধরনের ক্রিকেট থেকে বহিষ্কার করতে হবে।এই দাবি দফার সাথে যুক্ত করলাম। কোটি বাংলাদেশীরা বাংলাদেশের অক্সিজেন খ্যাত বিসিবিকে এসব দুর্নীতিবাজ থেকে বাঁচাতে ঐক্যবদ্ধ হও।✌✌✌,1,sports
এই সালা কুত্তার বাচ্চা তুই ত আসল নস্ট,1,sports
মাগীদের আর কি বলবো এরাই সকল নষ্টের মূল।এদের কারনেই সাব্বিরের মতো একজন প্রতিভাবান ক্রিকেটার আজ লাইনচ্যুত।,1,sports
তোর মাইয়ারে চোদি হালার পুত ভুয়া নিউজ কেন দিস,1,sports
কুত্তার বাচ্চা কুত্তার বাচ্চা কুত্তার বাচ্চা ভারত এর সাথে জরিতসাকিব কে নিয়ে নোংরা খেলা খেলছে।পাপনের গালে আগে জুতা মার।সাকিব কে বছরের জন্য নিশিদ্ধ করেছে। এক বছরের সাজা বাতিল।,1,sports
"চুদির বেটা রুবেল
",1,sports
শুয়োরের বাচ্চা পাপন কে লেংটা করে বাহির করা উচিত,1,sports
আরে তরা খেলুয়ারদের টাকা দিবি কেন কেছিনো চুদাওগা,1,sports
শালা তুই নাম্বার ওয়ান বাটপার,1,sports
সালারে জুতা মার,1,sports
খেলা চোর মাদারচোদ রা,1,sports
সব গুলার বিচির মধ্যে হাতুরি দিয়া বারি দিয়া জীম ধরাই দিতে হইবে৤ তেল বারি গেছেমাংচোদ,1,sports
বালের খেলোয়াড় মুশফিক,1,sports
জামাত শিবির কর্মী কুলাঙ্গার আজহারির কিছু কুফরি আকিদা বা বিশ্বাস যা মুসলমানদের আকিদা থেকে ভিন্ন।,1,sports
আবাল,1,sports
পাপন শালা হচ্চে বিসিবির প্রধান দূর্নীতিবাজ। তার পদত্যাগ চাই।,1,sports
সিলেট হেডার টিম বানাইছে সালা খানকির পোলারা হোগাদ্দেক বুজি আবার ক্যাপটেন,1,sports
শালা পাপনের বাচ্চা তুই এসে ক্রিকেটকে ধংশ্শ করে দিছোত। শালা মাদরচোদ তারাতারি পদত্যাগ কর।,1,sports
সালা অনেক লুচ্চা ...................,1,sports
পাপন একটা খানকির পোলা,1,sports
মাগী বাজ খেলোয়াড় কে কেন বিছিবি রাখে। সব গুলা মাদক সেবন কারি। বস্তি থেকে উঠে আসলে এমনি হয়। পরিবেস বদলালেও নিজের অস্তিত্ত বদলাতে পারেনা।,1,sports
নাহিদ পাগলা।তুই হাত মার হাত মারলে মানুস হবি।।পাগলু।।ভারাত এর সোনা৷ চাটা৷ কুত্তা,1,sports
রুবেল একটা জারজ সন্তান<br />ঠিক আছে !<br />শালা একটা পাক্কা বেয়াদব <br />ঠিক আছে !,1,sports
শালা পাপন তুই আসলে একটা বাইঞ্চোদ হারামজাদা,1,sports
তুই একটা বাইঞ্ছদ শালা খানকির পথ তুই সোনার ইউটিউবর,1,sports
সুজন। আকরাম। দূরজয়। কুয়াবের কুত্তার বাচ্চা ওরা সব কে বহিসকার করা হক,1,sports
এই মাদারচোদ বছর নিসেধাজ্ঞা দিছে নাকি বছর দিছে?উল্টা পাল্টা নিউজ দিয়া মানুষ কে বিভ্রান্ত করস ক্যা?,1,sports
সাকিব আল হাসান ঠিক আছে ঐ পাপন মাদাররির পুত কে বহিষ্কার করতে হবে,1,sports
পাপনতোমার ;বাপ আর মা; ভালো মানুষ ছিলেন। কিন্তু তুমি কি হইলা এ ঘরের ঠিক বুঝলাম না। এত ক্লাসলেস কি করে হতে পারে মানুষ! এই দেশের মানুষের কাছে তোমার গ্রহণযোগ্যতা অনেক আগেই শেষ হয়ে গেছে। তারপরও কেনো ছেচরামি করে নির্লজ্জ আর বেশরমের মতো পড়ে থেকে দেশের ক্রিকেট কে ধ্বংস করছো? ভাই তোমার মতো একজন পাপন সাথে কুকুরের বাচ্চা সুজনজালাল ইউনুসআর যারা আছেন নিজেদের যোগ্যতা ছাড়াই সব জান্তা গামছাওয়ালা হয়ে বসে আছেন আমাদের দরকার নাই। আমদের দরকার মাশরাফিসাকিবতামিমদের।,1,sports
নিয়মের বাইরে গেলেই শাস্তি এটাই নিয়ম ।আমরা বাঙালি চোরকে ভালো মানুষ বলি কারণে চোরি করে সে মসজিদ তৈরি করেছে ।সালার পাগলা মাদার চুদ,1,sports
বালের বোর্ড যত দিন পাপনের মত দালাল থাকবে তত দিন এমন করেই পিছিয়ে থাকবে বাংলাদেশ টিম,1,sports
পুরানা পাগলের ভাত নেই আর তুমি নতুন পাগল হিসাবে আর্বিভাব হইলা কোথেকে সালার দালাল চামচা ফলোআফ হওয়ার চিন্তা হইছে বুঝি?,1,sports
সব কয়টা হালার জারজ কুত্তার বাচ্ছা,1,sports
সিলেট টিমে নাজমুল হুসাইন মিলন নামে একটা আকান্দা রাম ছাগল আছে।। সে কোন যুক্তিতে টিমে চ্যান্স পায় আমার মাথায় ঢুকে না।,1,sports
আরে সালার পো সালারা সামান্য গালি নিয়ে এত্ত কাহিনি করস কেন,1,sports
হালার ঘরে হালা একটা গাজা খোর,1,sports
সব হালায় বাল পাকনা,1,sports
সব শালারা পাছায় জুতার বারে👠👠👠👠,1,sports
সালার পুত নিচু পরিবারের সন্তান ব্যবহার জানেনা,1,sports
বিসটা যদি গুজন থাকে তরা মাদার চুদেরা এত আগে আগে এত কথা বলছ কেন,1,sports
আরে এই মেয়েটা মাগি খানকি ওর ওনেক বিডিও আছে ও দেকছি,1,sports
পাপইন্না সালারগরে সালারে থেকে বাদ দেওয়া উচিত,1,sports
কি বাল গালি দিছে হে তাতে হইছেটা কি খেলতে পারে আমার সাউয়া খেলে। আবার বেতন বাড়ানের জন্য ফাল চোদায়।পাবলিক কিছু কইলে চামচামি করার চামচাগো অভাব থাকে না।,1,sports
আসুন আমরা সবাই মিলে এই চেনেল এর মালিকের মারে গিয়ে নিজ দায়িত্বে চুদে আসি,1,sports
রুবেল একটা খানকির পোলা তাই খাকির মত আচরণ,1,sports
পাপনের ওর বাপের গোয়া দিয়া হইছে তাই শাকিবের বেন লাগাইছে দুই বছর পর মাদারচোদ,1,sports
পাপন শালা সবছে ব্রানচুদ,1,sports
পাপনের পাচায় লাতি মারার সয়ম এসে গেছে 👇,1,sports
পাপন একটা কুত্তার বাচ্চা,1,sports
এমন পাপন বাজ দের জন্য বাংলাদেশ নষ্ট হয়ে যাচ্ছে এই রকম জানোয়ারদের কে দেশ থেকে বাহির করে দেওয়াটাই উওম।,1,sports
পাপনের মায়েরে চুদি,1,sports
ভাইরে খুব কষ্ট লাগে সাকিব না থাকায় সালা পাপন ষড়যন্ত্র করছে,1,sports
আমার মনে হয় রুবেলের রক্ত ও মশার মাসি খাবে না যে খালো চুদলেও চোদা যাবে না দেখতে কুত্তার মত লাগে কালো কুকুর,1,sports
মামা ক্রিকেটের হোগামারা সারা,1,sports
তুই হইলি বড় মাদারচোদ,1,sports
এই মাগির পেলা মিথ্যাবাদীএরে বাদ দেওয়া হোক,1,sports
হাংকির পুলারে পুটকিমারা হোক,1,sports
সাব্বিরের সোনা কাইটা ফালানো উচিত।তারপর ওর সোনা ওর নিজের পুটকি দিয়ে ভইরা দিতে হবে।কারন সোনার বিগারের চোটেই তো এত আকাম কুকাম চুদায়।,1,sports
এই আই সিসির পাচাটা গোলাম পাপনের মত ফইন্নির পোলারে নিশিদ্ধ করা হোক।।।,1,sports
সালারা মাটে বাল খেলেনা তাগ আবার বেতন বাড়াতে হবে আমার মতে খেলা বন্দ করা উচিত,1,sports
মারে চুদে নাকি সালা,1,sports
চামচা গো ধররা জুতা মার,1,sports
পাপনের বইন রে চুদি,1,sports
বাংলাদেশের আবাল ক্রিকেটাররা সাকিবরে ব্যবহার করে নিজেরা নিজ নিজ মত খেলা চালিয়ে যাচ্ছে।। আর ডেকির তলে মাথা গুজে দিছে ।। তামিমের ও খেলতে যেতে হবে আর সাকিব ও যাবে।। তারা না গেলে বাংলাদেশের একটা খেলোয়ারও যাবে না।।।,1,sports
কুত্তার বাচ্ছা পাপন্নের পদত্যাগ চাই,1,sports
তোমিতো বড় হারামজাদা কি করে লোকমানের পক্ষে সাফাই গাও। দেশি প্লেয়ারের টাকা কম কেন বিপিএলে বিদেশিদের টাকা বেশি কেন। নিজের স্বেচ্ছাচারিতা মত চালাচ্ছো।কেন খেলার আগেই প্রিমিয়ারলীগে জেনে যায় কে জিতবে কে হারবে।চোরেরমার বড় গলা পাপনতোমি চোরের দোসর।,1,sports
জার্সি পরা এই হালাতো বাবা খোর,1,sports
জানোয়ারের এর পরিছয়ে দিয়েছে তাসকিন,1,sports
পাপন কুত্তার বাচ্চাঁকে বোর্ড থেকে বাহির করা হক,1,sports
ঠিকই করছে শালার বেসি করে ওরা ইচ্ছামতো পিটানো উচিত ছিল,1,sports
পাপন কুত্তার বাচ্চারে জুতা পিটা,1,sports
এই মাখির পুএ তো করছে এরক আমি,1,sports
"শুয়োর টিভি, বালের নিউজ ।",1,sports
হালা তুই একটা মদন,1,sports
তোর মায়ের সাওয়াত হ্লল দিয়ে আমন চোদা দিব পরে র এলা নিউজ বানাবি না মাদ্র্ছদ,1,sports
শালা ফকির,1,sports
ভাই একটি ভিডিও প্রচুর ফেসবুকে শেয়ার হচ্ছে পাপন নাকি জুয়া খেলে কিছু কিছু খেলে শালা মাদারচোদ খানকির পোলা ওই সাকিবের জীবনটা শেষ করে দিয়েছে অনেক ভালো মানুষ ছিল তো খারাপ হলো কিভাবে আমাদের দেশের সাংবাদিকরা তাদেরকে সাংবাদিক বললে ভুল হবে কেননা আপনার ভিডিওটা কেউ প্রচার করে না♦♥♠♣,1,sports
আপনি একটা আবাল,1,sports
খানকিপোলা এতো গালি খাস তার পরও ভিডিও ছাড়স কেন মাগির পুত,1,sports
কে কে পপনকে চুদবেন হাত তুলেন,1,sports
পাপন বাজা একটা বে জর্মা,1,sports
ওরা জন মিলে তাসকিনের থাপ্রাইলে ভিডিওটি আরো ভাল হত।আবালের দলগুলো।,1,sports
"নাসির খানকির পোলা এই রুবেল বাইঞ্ছদ এর মুরিদ
",1,sports
তাসকিন হালার পোলা যে পাগলের চুদা পোলাপাইন তা আবার প্রামান হলো,1,sports
সালারে ত দেখতে চোর মনে হয়,1,sports
এটা পাপন খানকির পোলার নাটক,1,sports
মাদার চোদেরা তোগোরে গালি দিছে।মুশফিক কি তোগো বাবা লাগে। মুশফিক কে।,1,sports
পাপন কে জুতা দিয়ে পিটিয়ে বিসিবি থেকে বের করে দেয়া হউক,1,sports
ওই ছেলে টার পাসে বাংলাদেশের জারছি গায়ে ওই বানচোদ কিছু বুঝে না কিছু না ওই ছেলে টাকে চোরের মত করে ধরে রাখছে কেন সালা মাদারচোদ বাংলাদেশের জারছি গায়ে দিছে সালা গাজা খাই মাটি খেয়ে নিশা করে,1,sports
ছাব্বিরকে বাদ দেওয়া হোক,1,sports
তাসকিন কুত্তার বাচ্চা তুই😡😡😡,1,sports
কুওার বাচ্চা তুই দেশের ক্রিকেট ধ্বংস করবি তুই ইন্ডিয়ার দালাল আমার দেশের ক্রিকেটকে ধ্বংস করছিস তোকেজুতা পিটা করে বিসিবি থেকে ভের করা হোক,1,sports
কিছু কিছু বোকাচোদা আছে যে হিরো হিরোন নাম দিয়েওননো হিরো হিরোইন বই চালায়,1,entertainment
আলীরাজের বউটাকে ল্যাংটা করে বাশ দেয়া দরকার ছিল।,1,entertainment
বুদা ভাড়া দিয়ে দুধ বড় করতাছো এই টা ঐ শুনছিলাম তাই তো বলি দুইতালা এত বড় সুন্দর কেমনে হলো যাক টাকা বেশি পাইছো,1,entertainment
শালিরা চোদা খাওয়ার পাগল,1,entertainment
শালারা অস্ত্র দিয়ে যে গান বানাইচোচ এই অস্ত্র গুলোর নাম বল,1,entertainment
তোমার মতো ভাবী যদি আমি পাইতাম কুকুরের মত ছাইজ করতাম শালী,1,entertainment
নাটকের পরিচালক একটা রাম ছাগল এটা দিয়ে কি বুজালো আর কি বা মানুষ শিখলো। ছাগল কোথাকার।,1,entertainment
"এ সমস্ত নির্মাতা কলাকুশলী কারা, হালারা ভোদাই নাকি",1,entertainment
বাংলার নতুন নটি। মাগি,1,entertainment
মাদারচুদরা কি অডিশন করস নাকি মানুষকে অপমান করস,1,entertainment
ঐ মাদারচুদ গল কি ছবি দিলি আগা গুরা মিল নাই।,1,entertainment
তোর থেকে ফারিহা অনেক ভালো আছে খানকি,1,entertainment
মমকে আর ফারিয়াকে কুত্তা দিয়ে চোদানো দরকার আর ছেলে দুইটাকে হিজলে দিয়ে চোদানো দরকার,1,entertainment
একটা মাগির আলাপ শোনার চাইতে ভাল সেক্স ভিডিও দেখলে আরো ভাল কারণ দুটোই একরকম 😪😪😪 টাট্টি মার্কা মাইয়া এইটা,1,entertainment
এসব কিরে ভাই ছাগল নাকি হালায় 😡,1,entertainment
ভোদার মুভি শালারা।এই গুলোকে কোন সিনেমা বলে । আবালের দল। এর থেকে তো পাড়ার দাদী নানী রা অনেক ভালো গুল্প বলতে পারে,1,entertainment
খানকি আবার জাত আছে নাকি হিন্দু কি মসলিম কি,1,entertainment
বিচারক মাসুদ রানার বিচারকদের যে পাঠাইছে তারা আসল খানকির বাচ্চা মাদারচোদ না হলে এই সমস্ত অসভ্য মানুষকে বিচারক হিসেবে কেমনে পাঠাইছে,1,entertainment
এগুলো ফুতফাতের মেয়ে এগুলোকে100 টাকা দিলে ভোগ করা যায় সানিতা সামনে অনেক বড় মাগী হবে,1,entertainment
দাড়ি ওয়ালা তো এক নাম্বার বাইনচোত আর বাকি গুলা রে জুতা মারা দরকার,1,entertainment
আচোদা বিচারক,1,entertainment
দাড়ি আলা জাজ টা কে অই সালারে তো চিনিই না,1,entertainment
মানুষ যে বাংলা সিনেমা দেখেনা একদম ঠিক আছে। গাধা গর্দভ মাগীবাজ বেশ্যাগুলোরে দিয়ে নাটক আর সিনেমা বানালে সেই নাটক আর সিনেমা রাস্তার গরু ছাগল ছাড়া আর কেউ দেখবে না। মোস্তফা সারোয়ার ফারুকী তৌকির আহমেদের মতো মানুষরা ঠিক করতে পারে কে হবে মাসুদ রানা। তা না করে দুইটা মাগীকে দিছে বিচারকের আসনে সাথে দুইটা মাগীখোরকেও। শবনম ফারিয়া একটা বুটকি হয়ে কিভাবে অভিনেত্রী হয় আবার ছবি করছে মাত্র একখান। ভাভাগো ভাভা দেশে আর কোনো অভিনেত্রী ছিলো নাগো ভাভা !!!! আর মম তো হইছে আরেক বেশ্যা। এখন তো সিনেমা করতে পায় না কেউ নেয় না বিগ বাজেটে বিছানায়। দুই মাগী করছে এতোদিন নাটক এই দুই মাগীরে দিছে নায়ক সিলেক্ট করতে। নিজে ভাত খাইতে পায়না পরের চা খাওয়ার ভুল ধরে। আর একটা মাগীখোর নাটক পরিচালকরে দিছে বিচারক। যত বালছাল মার্কা নাটকের পরিচালকরে বানাইছে নায়ক সিলেক্ট করার জন্য। গাই দিয়ে কি হাল চাষ হয়। বিচারক হতে পেরে এমন ভাব এক একটার মনে হয় যেন তারা না জানি কয়বার অস্কার পাইছে। যত সব ভোদা কারবারির কান্ড কারখানা !!!!,1,entertainment
দূই জন পতিতা মাগী নাম্বার এক কারন মা আগে করছে পতিতা মজা টিভি খানকি পুত শালা,1,entertainment
শালার মুভি এটা নাকি নাটক।,1,entertainment
বালের জাজ।। আর এই গুলো কোনো অডিশন হইলো লোক ডেকে নিয়ে শুধু অপমান করছে।। আর কয়েকটি বিচারক হইছে মনে হয় জুতা দিয়া পিডায়।। 😡,1,entertainment
দারি আলাকে কুত্তা দিয়া পোনদা,1,entertainment
ওর মায়ে হোইবো মাসুদ রানা মাগির পোলা আর মাগি,1,entertainment
আরে মাগি তোরমায়রে চুদি মাগির বাচচা মাগি সানাই,1,entertainment
কুত্তা মার্কা ব্যাবহার শালার,1,entertainment
শালা গাঁজাখোর মাদারচোদ,1,entertainment
নিপুন একটা খামতি খারাপ মাইয়া,1,entertainment
"আর কাওকে পেলো না হিজড়া jaky, souvik দের নিয়ে natok বানিয়েছে. Tisarনামটা দেখে প্লে করছিলাম. কিন্তু হিজড়া, আবাল চোদাদের দেখে মেজাজ খারাপ হয়ে গেলো। play করাটা ভুল হলো",1,entertainment
এই মাগীরে ঘোরা দিয়ে চোদানোর ধরকার ছিলো,1,entertainment
নিরিহ কাজের মেয়ে পেয়ে আকাম করলো - মেয়েটাও সেই পদেরই,1,entertainment
তুই যত বার বাহ বাহ চোদাইসৎ ততবারেই তোরে থাব্রাতে মন চাইছে,1,entertainment
এই বিচারক না গাজা খোর প্রতিযোগি কে বলে সেলুনে যেতে আরে শালার বিচারক তুই যা সেলুনে যে অবস্থা দেখা যায় মনে হয় বছর সেলুনে জায়না শালা গাজাখোর বিচারক।,1,entertainment
ওই সালাত পুত ফকির নাকি চুল কাটার টাকা নাই শার্ট টা তো ফুট ফাত থেকে কিনছে,1,entertainment
ছাগলের তিন লাম্বার বাচ্চাদের বিচারক বানিয়ে বসে আছে,1,entertainment
দাড়ি মুখে যেই মানুষ নামে পশু অর নাম কি। মাদার চুদ তর মারে চুদ।আমি চুদি,1,entertainment
বস্তা পচা পোলা।<br />ডান্স টা ভালো ভাবে শেখ মাদারচোদ,1,entertainment
তোর মা বাবা ও খারাপ তোর মা মাগি ছিল তোরে ও মাগি বানাইছে,1,entertainment
হালার পো হালা এইটা কি ২০১৯ সালের নাটক????,1,entertainment
বোকাচোদা ঠিকমতো আগে কথা বলা শিখে আই। কথা বলতে পারোস না রোস্টিং ক্যামনে করোস,1,entertainment
খানকি তুই তো কোতো সুনা নিছোদ,1,entertainment
"মাগি একটা,এতোদিন ভাবছি সাকিব খারাপ।এখন দেখছি তুইই খারাপ।সাকিব ভালো কাজ ই করছে,তোকে ছেরে,তোর আসল রুপ বেরিয়ে পরছে",1,entertainment
বিচারক গুলোর নাম্বার পেলে ভালো হতো খানকির পোলা ও মাইয়ারে কে সাহস দিছে জিগাইতাম ছেলেদের কে অডিশনের নাম করে অপমান করার সাহস পাইছে কই,1,entertainment
কুত্তার বাচ্চা সানাই।,1,entertainment
"সাবিলা, এই বালটাকে দেখলেই মাথা হট হয়ে যায়..!",1,entertainment
বাংলার নতুন তসলিমা নাসরিন পতিতা,1,entertainment
পর পর ভিডিও😍😍 এই টা বেষ্ট ছিলো জাজ সালা আর সালি রা কি খেয়ে আসছে কে জানে এর বিচার হোওয়া দরকার,1,entertainment
এই নাটকের পরিচালক সালা<br />পাগলা,1,entertainment
রুবেল বাইনচোদ নাকি নায়ক!যত অসুস্থ ধারার গান আছে সবগুলো সে করেছে।,1,entertainment
পাগলদের কাঠগড়ায় দাড় করানোর জন্য ধন্যবাদ হেসে মরে যাই,1,entertainment
এই সাসোডিইরে আমিই হোদাই মাগিই কোনাই গার খান কিই আসতারা,1,entertainment
সালারে নোবেল ছুড়ে মার জাজ দের।,1,entertainment
হেডার টিজার আমিন খান দেখায় কম,1,entertainment
হিন্দু মালাউনের বাচ্ছা গরুর মুত খেয়ে এই নাটক পরিচালনা করেছে শুওরের বাচ্ছা।,1,entertainment
সব আবাল মার্কা বিচারক দিয়ে রিয়্যালিটি শো করা হয়েছে। সামনে পাইলে সবগুলারে জুতা পিটা করতাম। বিচারকের গোষ্ঠি মারি। ওদের কি বিচার করার যোগ্যতা আছে। চ্যানেল আই একটা ফালতু মিডিয়া। তোরা মানুষকে এইভাবে অপমান করার জন্য ডাকিস না। সবার একটা আত্মমর্যাদা আছে। আবালচোদার দল।।,1,entertainment
এই শালা ভিডিও মেকার অসম্ভব জারুয়া ।।বালের প্রতি ওনার এক অসম্ভব আকর্ষন ।।হা হা হা,1,entertainment
"আরা চোদা পরিচালক,কিভাবে লাশ মাটি দেয় সেটাও জানে না,সালারা লুচ্ছামি করতে আসে আর পাবলিকের টাকা হাতিয়ে নিতে আসে,আর এই রকম গর্দভ মার্কা ছবি কিভাবে রিলিজ দিলো?",1,entertainment
"বালের ছবি, নায়িকা গুলোরে দেখলে মনে হয় অষ্টেলিয়ান জার্সি গাভী আর দুধের জন্য সেরা হবে প্রতিযোগিতা করলে?????",1,entertainment
জুতা মা র শালা গরে।,1,entertainment
বিচারক না ফাজিল বেয়াদব।শালারা নিজেকে কি মনে করে চ্যাটের বা ল।,1,entertainment
মম কে আর সবনম কে আমার উচিতে গোয়ালন্দ ঘাট জাতীয় খানকি পারা পাঠানো হোক খুবই তারাতারি,1,entertainment
ছেলে।পগল।চুদা।মেয়ে।কানকি,1,entertainment
খানকির পোলা ভাইজান এর কাজ,1,entertainment
এই সালিরে চামিচ চুন খাওয়ান। পাগল চুতিয়া।,1,entertainment
কাংলুদেশ এরকম চোদানোাই পারে.....কেলানো মাস্টার.... !!,1,entertainment
ফাহমি পাঠা পুরাই জারজ ওর দাড়ী গোফ অার চুলের ষ্টাইল দেখলে মনে হয় পাবনা মেন্টাল হাসপাতাল থেকে উঠে অাসছে। অার রানা এখানে অাসছে ব্লোমোভির অ্যাক্টর খোজার জন্য। ফারিয়ার কথা কি বলবো ওতো অভিনয় বলতে কিছুই বুঝেনা। পুরাই ক্ষেত থেকে উঠে অাসছে। অার মম দেশ সেরা নর্তকী মম সানি লিওনের মত হতে চায়। তবে লিওনের মত সুন্দর না হওয়ার তার বেইল নাই। ভাল পর্ন তারকা হতে পারবেনা। ওর সাথে কোন পর্ন ছেলে অভিনয় করতে রাজি হবেনা!,1,entertainment
ওয়ারফেইজ চিনে না হালায়!,1,entertainment
এই দালাল মাগি মরার পরে কই য়াবেঅসুর জাতি,1,entertainment
শবনম ফারিয়া কে আমার কাছে পাঠিয়ে দাও! আমি একটা নতুন দুধের ফ্যাক্টরি খুলবো 🐸 আমি ওর সাথে একান্ত কথা বলতে চাই আমার খাস কামরাতে 🐸 বাণীতে 👉 জামালপুরের ডিসি 😂 টুকাই ফাহমি বেশ্যা ফারিয়া মমরা বিচারক রাবা খান লেখিকা সালমান মুক্তাদির অভিনেতা 🖕 মাননীয় স্পীকার এজন্য এই দেশের হোগা মারা সারা 🤔🖕,1,entertainment
বালের অডিশন বালের জাজ হালার পুতের চেহারার দিকে কি তাকানো যায়,1,entertainment
বালের বিচারক সব টি মাদারচুদ কাছে পাইলে জুতা দিয়া পিটাইয়া কপালের চেরা তুইলা ফালাইতাম অভিনেত্রী মম মাগির বাচ্চা,1,entertainment
দুধের পাহাড়,1,entertainment
বাংলাদেশের সংস্কৃতি নষ্ট করে দেয়ার জন্য এরকম আবালেরাই যথেষ্ট। আমাদের বাংলাদেশ আর বাংলাদেস নাই। আজম খানের ভাষায় এটা এখন ভাঙ্গাদেশ!!!,1,entertainment
এই নমরুদের বাচ্চার সোনাটা হায়না দিয়া খাওয়াতে হবে,1,entertainment
এমন কুত্তার বাচ্চাদের কে বিচারক দিছে কে। ব্যাবহার শিখিয়ে তারপর এদের বিচারক বানানো উচিৎ,1,entertainment
এই নাটকের পরিচালক একটা রামছাগল নাটকের অ আ ই কিছুই বুঝে না,1,entertainment
নষ্টা মেয়ে তোর মরনের ভয় নেই আল্লাহ তায়ালার ভয় নেই সমাজ ছাড়া বেহাপনা নটি তুই,1,entertainment
ডাষ্টবিনের ময়লা জাহান্নামের কিট,1,entertainment
হালায় কোন দেশি গাঞ্জা খাইছেরে ভাই,1,entertainment
ফাহিম ডাইরেক্টর না কি ওরে লাগে জংলি বন মানুষের মত না বানর শালা চুল বাল দাড়ি কিছুই করে না অন্যজনের হেয়ারস্টাইল চেহারা নিয়ে ব্যঙ্গ করে মিডিয়ার বেশিরভাগের ক্যারেক্টার এরকমই হায়,1,entertainment
চ্যানেল আই কর্তৃপক্ষ এসব আবালচোদা কুত্তার বাচ্চাগুলোকেই জাজ হিসেবে নেয়। এর আগেও গানের রাজা তে সেটার পরিচয় হয়ে গেছে 🤬,1,entertainment
"বালের নায়ক,,অপরাধী কে শাস্তি ছাডা নাটক আচুদা পরিচালক",1,entertainment
সব গুলো ফালতু আর নোংরা শুয়ের বাচ্চা আর মেয়ে গুলো বালের,1,entertainment
বিচারক গুলা একেকটা মাদারচুদ। সালাদের জুতা পিটা করে ভদ্রতা শিখানো উচিত।,1,entertainment
মাগিরে জুতা মারা দরকার।,1,entertainment
কোন মাদার চোদ দে এমন পরিচা লকওর মারে দিয়া এমন ছবি বানাইলে আর ভাল চলতো মাগীর পোলা,1,entertainment
খানকি নাইকা,1,entertainment
শুয়ারের বাচ্চা জাজদের জুতা দিয়ে পিটানো উচিৎ। মাদারচোদ,1,entertainment
নিচতলা ভাড়া দিয়ে দোতলা বড় করছে এটা আবার প্রকাশ‍্যে বলতেছে খানকি তোর চোদ্দ গোষ্ঠী বেশ‍্যা ছিল মনে হয়,1,entertainment
শবনম ফারিয়ার পাশে এই শোয়ারের বাচ্ছাটার নাম কি হালা নিজেও একটা খাইচ্ছর ভাল করে দাড়িকাট করেও আসেনি মনে হয় মাটির নিছ থেকে এসেছে। শালা বেয়াদব।,1,entertainment
তর মা খানকি তুই খানকি এই কুত্তার বাচ্চাটাকে মেরে ফেলা উচিত,1,entertainment
নায়কের নাম সাহের খান না হয়ে পাদের খান হওয়া উচিৎ ছিল যতসব ফালতু অভিনয়।,1,entertainment
শুয়োরের বাচ্চারা নিজের চেহারা দেখছে। আর ঐ মাগি র নাটক আমরা দেখি বলে ও ঐ খানে বসতে পারছে জাজ হয়ে।,1,entertainment
তুই একটা গাঞ্জাখর বোকাচোদা,1,entertainment
বেশ্যা মিথীলা নোমো মাগি,1,entertainment
খানকিরে নিচ তালা ভাড়া দিতে কস।।। কেন মানুসের কি ধর্ম নাই আল্লাহর প্রতি ভয় কি সবারি উঠে গেছ্র রে শুয়েরের বাচ্চা,1,entertainment
কি ফিগার কতো সুন্দর দুধ গুলো যেন বড়ো বড়ো ডাব ।সেক্সী বৌদি ।,1,entertainment
ওরে জয় ভাইয়া ওর জায়গায় কেউ জেতে পারবে কেমন কোরে ওর মতো নির জজ্জো না ওর দুধ দেখছে সবাই। মাগি একটা। ভাইয়া আপনার কথা গুলি খুব ভালো লাগছে।এখনো কাজ কোরতে পারলোনা ওনাকে কেউ ধোরতে পারবে না।ঠিক বোলছে ওর মতো খারাপ কেউ হোতে পারবে না।ও নাকি কিউট। হু ওর দুধের পালিস কোরাতে তো জেতে হবে তাই বড়ো লোক তো লাগবে।খানকি পানার একটা সিমা থাকা দরকার।খারাপ। ছি।,1,entertainment
এই শাউয়ার পোলা ফাউমি না শাউয়ামি এর হোগায় প্রচুর কারেন্ট আর আমার তো মনে হয় যে শাউয়ার পোলা মাইয়াগো বিচারক বানানো হইছে তারাও মনে হয়না মাসুদ রানা সিরিজ পড়ছে যদি পড়ে থাকে তাহলে বিচারক হওয়ার পরে পড়ছে। আর একটা জিনিস বুঝলাম না মাসুদ রানার ক্যারেক্টর প্লে করতে গেলে যে মাসুদ রানা সিরিজ মুখস্থ করে আসতে হবে এমনতো কোন কথা নাই আর এমন কথা থাকলে বাইরের আর্টিস্ট কাস্ট করা হবে তারা নিশ্চই মাসুদ রানা সিরিজ পড়েনি,1,entertainment
ওই মাদারচুদের চুলের কি অবসথ্যা তুই বিচারক কেমন হলো,1,entertainment
বাংলাদেশে গরীব লোক না খেয়ে মারা যাচ্ছে আর এই মাগির বাচ্চা দুধ বড় করার জন্য এত টাকা ব্যায় করেছে । তুইত টাইরেক জাহান্নামি হয়ে গেছত। কারন পৃথিবীর সবাইকে জানিয়ে দিলি তোর দুধ বড় করেছ। আবার দেখ আল্লাহ তোমার এই বেপর্দা দুধের ভিতর এমন রোগ দেয় পরে আবার তোমার এই দুধ কাটতে হয় কিনা দেখ।,1,entertainment
মাগীকে এক রাত কাছে পেতে পারলে কোটি দেব,1,entertainment
ভাই মাসুদ রানার বাল গুলা কেমন ছিল আমি ওর বালের মত বাল রাখতে চাই,1,entertainment
মশারফ করিমের নাটক মানে মেয়েদের দুধ দেখান,1,entertainment
মাদার চোদ সো,1,entertainment
পা ধরে তোর হোগা ফাড়বো শালা,1,entertainment
তোমারে পাগলা কুত্তা ও চোদে না তুমি রংপুরের অভিসুপ্ত নারী বেয়াদুব মেয়ে,1,entertainment
এই সালায় পাগল,1,entertainment
চুরের মত বেডা গাঁজা খুরটার নাম কি,1,entertainment
নায়ক মানে চাগল,1,entertainment
গর্ভাবস্তায় আয়োডিনের অভাব থাকলে এমন খানকি মার্কা বিচারক তৈরী হয়।।।।।,1,entertainment
তুই রাছতার মাগি,1,entertainment
পপি কে লেংটা করে মিশা রেপ করলে seen টা অনেক সুন্দর দেখাত।,1,entertainment
মাগী,1,entertainment
আসলে ব্যাপারটা হল এখানে গুটি কয় এক নটি এবং নটির দালাল বসেছে যারা কিনা ওদের মত নটি বা বেস্যা খুজতে এরকম পথ বেছে নিয়েছে কিন্তু সেটা তারা খুজে পাচ্ছে না তাদের লাগবো নটি যা ওরা করেতে পারে,1,entertainment
বালের বিচারোক এরা,1,entertainment
কুথায় থেকে এ পাগল ছাগল দরে আনে ছেনাল বুজলাম না।।,1,entertainment
মাদারচোদ বিচারক কে দেখলেই মনে চায় ভালোকরে পেটাই,1,entertainment
শালায় নিজে একটা বন মানুষ সে মানুষ দেখলেতো এমন করবেই,1,entertainment
সব কয়টা মাদার চোদ,1,entertainment
আমার কাছে বছর পুরনো ছিড়া জুতা আছে কাউকে মারার জন্য খুজছি আমাকে কেউ একটা চান্স করে দিবেন এদের কে একটু মারতাম সালা এদের মা বাবা পড়াশোনা করাইছে রাস্তায় আর দারি আলাতো গাজা আর বাবা খেয়ে আসেন এইখানে সালা,1,entertainment
মাগির মুখে রাম নাম তোদের গোয়ায় গন্ধ নুসরাত ফারিয়া যেমন তোর মাগির ও তেমন সানাই মাহবুব না মাগী,1,entertainment
তুই একটা চুদানি খানকি মাগি 😠😡😠,1,entertainment
আমি নতুন দাত লাগাবো এক ডিলে পাখি মারবো দাদ ঠিক করার সময় জখন ব্যথা পাব দুদ ধরে বলবো ওওওওও নায়লা ফাক উ।,1,entertainment
এরা তো মোবাইল গুতাতে ব্যস্ত। বালের বিচারক হইসে,1,entertainment
অই শালায় আমার চুলের জাজ,1,entertainment
কুত্তার বাচ্চারা কি বানাইছে এইডা কেউ অর বিচি চাইপা মাইরা ফালা,1,entertainment
উপরে সুদর ভোদা খুবই কাল,1,entertainment
পাডার বাল।সালারা মাথায় যা আবোল তাবোল আইছে তাই এ লেখছ।সালা মফিজএর দল।তোগো পাছা কালা না ধলা তাতে আমাদের কি।সেইটা আবার গানের এ লেখা লাগে কিসের জন্য। পাডা আবাল বলদ হাম্বা গরু মফিজ বাল বাল গান গায়।যেমন গান তেমন গানের গলা,1,entertainment
পাষা একটা মাদারি,1,entertainment
"ভাবতে অভাক লাগে, এক বছর আগে লেংটা হয়ে নাছানাছি করছে, আজ তাই এত বড় হইছে, কি করে হল, নিশ্চয় ছেলেদের হাতে টিপাটিপি করে, এটা বিশ্ব বড় মাগি হয়েগেছে, হায়রে মহিলা, আল্লাহ পাক তরে কত সুন্দর করে বানাইছে, আর তুই টাকার জন্য দেহ ব্যবসা করতেছো, মুসলিম কী জানিনা, যদি হয়ে থাকো তাহলে আল্লাহকে ভয় কর, মরার পর বুজবে কি অবস্তা হয়, এখনো সময় আছে এগুলা ছাড়,",1,entertainment
যত্ত সব ফালতু দেশটাকে বরবাদ করেদিল সালারা,1,entertainment
সালি একটা মাল ফুটকি মারতে ভালো লাগবে,1,entertainment
লাত্তি মার এই বুইড়া আবালগুলারে,1,entertainment
সৃজিতকে কুত্তা দিয়ে চোদালে বুঝতে পারবে ভার্জিন কে ছিল😂😂😂😂,1,entertainment
বাংলা ছবি এমনিতেই দেখিনা আবার মাসুদ রানা চোদাতি আসছে জনগন পাগল ছাগল,1,entertainment
শালাদের কেউ পেটা বে,1,entertainment
আমারে একটু বেশি চুদবার দিবেন।,1,entertainment
আপু ঢং দেখাইতাছো কেনো এত্তো যে ভাব চুদাইতেছো কেমেরার সামনে,1,entertainment
মাদারচদদের কেউ ব্যবহার শেখা।গাজা খাইয়া জাজ হইছস।খানকিরপুলাদের থাপ্রান উচিত। আফ্রিকা থেকে আসছে এইগুলি।আর রাসেল রানা যে মাসুদ রানা হওয়ার পথে তার সাথে কি ব্যবহার।,1,entertainment
সানাই বানাই কানাই পানাই তর মুখে ইসলামের কথা মানায় না তুই সরাসরি দুধ দেখাবি আর তরে নিয়ে ওয়াজে বয়ান করাটা ঠিক হবে না তর মুখে এটা মানায় না মাগি,1,entertainment
সালাউদ্দীন লাভলু সালা নাস্তিকের বাচ্চা।,1,entertainment
আবাল নায়ক,1,entertainment
বোকাচোদা বিচারক দিয়া অনুষ্ঠান করেন,1,entertainment
এই পতিতার মুভি কে দেখবে,1,entertainment
অই খানকি মাগি তকে চুদলে অ দন খারাপ হবে,1,entertainment
মাগীর কত্তো বড়ো দুধ 😵,1,entertainment
বালের জাজ বালের শো বালের প্রডিউসার বালের ডিরেক্টর।শো করার জন্য আগে শেখা জরুরী। সব গুলারে ডাইরেক্ট আফ্রিকায় পাঠানো উচিত।,1,entertainment
চুলদাড়িওয়ালা পকিন্নির ফোলার পশ্চাৎ দেশে দুইটা সিদ্ধ ডিম ডুকাইয়া রুটি খোলায় দেয়া তাপার উপড় বসায়া রাখা দরকার। 🤬,1,entertainment
সাকিবের নাছ মেয়েদের মত বাল লাগেনা ছাগল সাকিব,1,entertainment
জারা এক জামাই ছেরে অন্য জামাই খোজে তারা খানকি৷ মাগি তো সখ রে দেখলে তাইমনে হয়,1,entertainment
উ আমার হিজলা সাকিব খানরে,1,entertainment
ইচ্ছা করতাসে এই বিচারক নামের কুলাঙ্গারদের ধরে জুতার বারি দি। সালারা ভাবে কি নিজেদের মানুষকে এইভাবে অপমান আর হেয় করার অধিকার তাদের কে দিসে আর এই চুল দাড়িওয়ালা আমাজন জঙ্গলের প্রাণীটা আবার কেডা জীবনেওতো এরে দেখলাম আর এই হালা চুতমারানির পো আইসে অন্যদের জাজ করতে,1,entertainment
এ একটা মাগি এর নাটক <br />আমি দেখিনা ওর চোদাচোদির ভিডিও আছে নষ্টা,1,entertainment
বিচারক গুলো সবগুলো মাদারচুদ বাইনচুদ খানকির পোলা তদের কোন অধিকার নেই প্রতিযোগীদের অপমান করা বিচারক দের জুতার মালা পড়িয়ে ঘাড় ধাক্কা দিয়ে সাথে লাত্থি মেরে বের করে দেওয়া উচিত👡👡👡👢👢👠👠👠👞👞👞,1,entertainment
পভা খারাপ মেয়ে,1,entertainment
এইসব ফালতুশো এসে নিজের সম্মানটার সাথে তার আত্নবিশ্বাসও চলে যায় আদৌ কি এরা জাজ হওয়ার যোগ্যতা রাখে নিজের খুব বড় মনে করে এতটা বড় মনেও শারুখ খানও করে না আমাকে কেউ টাকা দিলেও এইসব বালের শো তে যাবো না,1,entertainment
আর বেশি দিন বাকি নাই যে দিন বিডি তে বাসর রাতে কেমনে চোদাচুদি করতে হয় তার একটা লাইভ প্রোগ্রাম হবে।।হায়রে নারী,1,entertainment
এই দাড়িওয়ালা শালাকে দেখে মনে হয় কয়েক বছর গোসল করে না অত একটা নেশাগ্রস্ত হাফ পাগল,1,entertainment
"জুতা দিয়া পিটাইলে শুধ হবে না মাগি কনকার,,, এরকম স্বার্থপরদেখিনি",1,entertainment
তোরা দুই মাদারচোদ নিজের পুটকি সাফ কর খানকির পুত,1,entertainment
আমার পাছা কালা তুর পাছায় ডুকামো মোটা বাঁশের পুটকি হ্লা।,1,entertainment
কোনো মেয়ে ইমু সেক্স করতে চাইলে যোগাযোগ করুন<br />01640087079 imo,1,entertainment
চ্যানেল আই এবং এসব আবাল সুদা বিচারক নিয়োগ কি করে দেয় বুঝি না তার কি মাসুদ রানা প্রতিযোগিতা শুরু করছে । না কি সাধারণ মানুষ কি ইনসাল্ট করছে বুঝি না কাতার থেকে দেখছি অনেক দিন ধরে শুনছি কে হবে মাসুদ রানা ।। কিন্তু দেখি অন্য কিছু । এইসব চ্যালেঞ্জ বিরোধে আইনি ব্যবস্থা গ্রহণ করা উচিত ।।,1,entertainment
শুওরের বাচ্চারা বিচারক হইছে। শালারা সব বাইনচোদ,1,entertainment
গাজিপুরের মেয়েরা চুদা লইতে পাগল,1,entertainment
ছাগলের বাচ্চা সাকিব খানের ছবি নকল করেছে পরিচালকের বাচ্চা তর বাপে নি ছবি বানাইছে,1,entertainment
হালা গিদরের বাচ্চা,1,entertainment
বাংলাদেশের আবারো একটা মাগি এসেচে তোদের বিচার আল্লাহ্ দেখবি এ দুনিয়াতে করবে,1,entertainment
আমার সাথে যারা এক মত। ফারিয়া ও মোমো ও হনুমান বানর ইদুর এদের কে জুতা মার চুদে। চ্যানেল আই থেকে বাহির করে দাও।,1,entertainment
এরা হয় কি ভাবে জাজ সব কয়টা ছাগলের বাচ্ছা এর থেকে জাজ,1,entertainment
হালার পো আগে তোদের চুল দাড়ি কাটা মাদারচোদ জাজ,1,entertainment
বিচারক ভাই মাসুদ রানা র কি ধোন টা বড় ছিল। যা ওদের নাই। সালার পাগল চোদন বিচারক 🖕,1,entertainment
নাটোরে ভিতরে কি ধনের বাজনা দেস। নাটক দেখতে ইচ্ছা করে না,1,entertainment
বাইনচোদরা এইসমসত করে মানুষের সুখের সংসার নষট করে দেয়।,1,entertainment
শালারা বিচারক নামে কলংক,1,entertainment
"আবাল নায়ক, শাবনুর আপুর জন্য ছবি টা দেখতেছি, আগের কোন নায়ক হলেও তো ভালো লাগতো যেমন, রিয়াজ, আমিন খান, বা অন্ন কেও, আর এটা কি নায়ক, অভিনয় ঠিক মতো পারে না😠, কই শাবনুর আর কই এই নায়ক😒😒",1,entertainment
এ সব পাগল ছাগল বিচারক হাই রে বাংলী বাচ্চারা খানকির পোলা রা তাদের কে জুতা দিয়া দাঁত সবটা পেলা দেয়ার দরকাল,1,entertainment
নাইস ভিডিওচুদাচুদি,1,entertainment
ইউটিউব এর মধ্যে এরকম মাগির গান কেমনে দে,1,entertainment
শালারা এইসব ভিডিও আজকালে দেখে,1,entertainment
সালার পূতের সালিরা চৌদ্দ বিয়ে করে নিজেদের কে বড় মনে করে,1,entertainment
জাজ দের কে আমি চু পাচা দিয়া মরিচ দিলে কেমন লাগে সালা মাদারচুদ,1,entertainment
মাগি তরে গিয়া লাগাতে চাই,1,entertainment
বিচারকদের নিজেদের চাহারার নাই ঠিক।তারা বালের বিচারক,1,entertainment
ওই ভুদার বেটা তুই একটু পর পর এমন বাহ্ বাহ্ চুদাস কেন,1,entertainment
আর পাসে জে মহিলা এগুলো মগিলা নয় এগুলো হিজলা,1,entertainment
মাগিদের জালায় বিদেশে এসেও শান্তি নাই আজকের পর থেকে নরমাল ফোন ইউজ করবো,1,entertainment
কুকুর দিয়ে চাটা শালি,1,entertainment
"পরিচারক কুত্তার বাচ্চা মুনাজাত নিয়ে মঝা করছ,, ধর্মীয় বিষয় নিয়ে মঝা করা ঠিক না.!!",1,entertainment
সব আবাল আর মাগি,1,entertainment
আল্লাহ্‌র নাম মুখে নিবি না খানকির মাইয়া,1,entertainment
কোন সালা পরিচালক নায়কের ভুমিকা নাইকাকে দিছে,1,entertainment
কুত্তার বাচ্চা 😠😠,1,entertainment
"আমি সানিতাকে ৩ ঘন্টায় ৫ বার চুদেছি, ফরেন স্টাইলে পাছা দিয়ে ও দিয়েছি মাত্র ৮০০০ টাকার বিনিময়ে, কেউ চুদতে চাইলে নাম্বার দেও আমি ব্যাবস্থা করে দিব, ওকে চোদার ভিডিও আছে আমার কাছে,। ভোদা চুইদা মজা নাই তাই গোয়া মারছি, দুদ অনেক টাইট।",1,entertainment
টাকার জন্য এরা কিনা করতে পারে আয় তুরে চুদি টাকা দিবো,1,entertainment
শালার দাড়িগোঁফ গাজা খোর বাদ দেন,1,entertainment
ওই বেটি সবাই কে চোদা দে।তোর খুব শখ,1,entertainment
নাটকের পরিচালক একটা পাগল কই থেকে আসে এই সব লোক ফালতু সব,1,entertainment
সনিতা একটা মাগি,1,entertainment
তুর মাকে আমি চুদবো মাগির পুত এগুলা কি গান।,1,entertainment
মিথিলা একটা বেশ্যা,1,entertainment
জুতা মার আবাল মার্কা বিচারকদের।।নাটক করার যোগ্যতা নাই এরা আইছে বিচার করতে।।,1,entertainment
এই তাদের নাটক দেখতাম কিন্তু এখন আর চুদব না সালা কুত্তার বাচ্ছা গুলা,1,entertainment
সব কটা কুত্তার বাচ্চা,1,entertainment
তোর মারে চুদি,1,entertainment
এটা পুরাই পাগল এটা কে না আনাই ভাল ছিল। খুব বাজে মেয়ে এবং দুশ্চরিত্রা ।,1,entertainment
এই খানকির পোলারা বিচারক হয় কিভাবে এভাবে মানুষদের অপমান করা একদম ঠিক হয়নি। চ্যানেল আই অনেক নিচে নেমে গেছে এরকম ফালতু লোকদের বিচারক হিসেবে আনা উচিৎ হয়নি,1,entertainment
নায়কের ছাগলের মত লাগে,1,entertainment
নেশাগ্রস্থ স্যারকে বলতে চাই কে তুমি বৎস ধরিয়া মৎস বেচিয়া গন্জে অকুলও কুন্জে না খাইয়া তাজা কেনো ভক্ষন করিয়াছো মেয়াদ উওীর্ণ গাজা,1,entertainment
ভাবতাম বাংলাদেশের ভালো একটা সুনাম ধন্য এইসব তার ছেড়া আর নোংরা ডাষ্টবিন এর পাশে থাকার যোগ্য ও না বাল পাকনা রা যদি হয় জাজ এমনিতেই কেউ বাংলা ছবি দেখে না নাটক যাও দেখতো তাও আর দেখবে না ভারতের রিয়ালিটি শো যদি কেউ দেখে থাকেন তাহলে অব্যশই বুঝবেন ভদ্র তা কাকে বলে মম আমার পছন্দের ছিলো ব্লোক করে দিলাম,1,entertainment
বিচারকের মায়েরে চুদি 😡,1,entertainment
চুদতে তারিখ,1,entertainment
নায়িকার দূধ দুটো সুন্দর,1,entertainment
আগে দোষ দিবো চ্যানেল আই কে এই পাগল ছাগল বিচারক আমার বালের বিচারক এই খানকির পোলাদের ছিড়া জুতা দিয়ে মারতে হবে।,1,entertainment
সালা সাফাত বুড়ো তোর মুখে সানায় দুধ ধুকিয়ে দোম আটকিয়ে মেরে দেবে😁,1,entertainment
নির্লজ্জ্ব সয়তানি।মাগিপনা সমাজের বাইরে গিয়া কর খানকি মাগি।স্তন ভোদা দেখিয়ে নাম কামাতে চাস।,1,entertainment
ওই খানকির পোলাকে আমার কাছে পাঠাই দাও আমি ওকে হিরো বানামু,1,entertainment
বুড়ি মাগী,1,entertainment
বালের সো।,1,entertainment
এসব বিচারকের মাইরে আমি চুদি জাজ মাল্টিমিডিয়া ওকে চুদি ইন্টারভিউ নাম করে এখন সবাই ধৌকা দিছে তোদের মাইরে মাপ!,1,entertainment
সৃজিত হালারপোরে বলি মিথিলা যদি ভারজিন হয় তাহলে বাচ্চাটাকি তোর মার পেট থেকে হইছে ?,1,entertainment
সানিতা কতটা ভালো ছিল এখন মাগি হয়ে গেছে,1,entertainment
আসলে মাসুদ রানা টা কে কে এই বালের রানা শুনি আগে,1,entertainment
এমন বোকাচোদাদের কে বিচারক বানাইছে,1,entertainment
তোর বোন কে চুদেছি,1,entertainment
মানসিক প্রতিবন্ধি ইউটিউবার,1,entertainment
শায়লা সেই দুধ আর পাছা,1,entertainment
খানকি মাগি বাংলাদেশের মেয়ে আমাদের ভারতের হিন্দি ভাষা বলে তাও আবার সব ভাষা ভোল পাগল জত,1,entertainment
পারলে দেশের জন্ন কিছু কর খানকির বাচ্ছারা সুদু আকাম করছ,1,entertainment
আমি তোকে এক রাত চোদতে চাই কারন তোর রেট কতো বল মাগি একানে আসে ইসলাম সিকাও মাগি ❌❌❌❌ 🌶🌽🍌 তুই পাম্পে জাইয়া তেলনে মাগি,1,entertainment
হালারা নকল করে। বালের ছবি,1,entertainment
সালাগো ভাবের চেয়ে ভঙ্গি বেশি সপ গুলি ইতর,1,entertainment
এসব হিজরা গায়ক কোথায় থেকে যে আসে ওরা 😡😡 দেশের টা বাজায় দিছে আমার ত মনে হই ওর পয়দার মধ্যে দুষ আছে এটা কি রে আবালচুদা তর পাচা বাদামি আর তুই হালার পুত হালা খাসির মাংস হাস না এগুলা কি তরে চুদার জন্য আইটেম দিছত 😂😂😜,1,entertainment
তুরে কোন সালা জন্মদিচে তুর দিগেকি তুকে বাবা তাকায়,1,entertainment
তার মত বিচারককে লাথি মারে চেয়ারের বাইরে ফেলা দরকার বাইনচোদ,1,entertainment
শালি এত খারাপ দেখলে বুজাই যাইনা,1,entertainment
সুন্দর মাগী,1,entertainment
দারুণ ছিলো👍 বাকি মালগুলোকে নিয়েও চাই। ওখানের ডিমপাড়া মুরগী শবনম ফারিয়া মাজারের খাদেম ফাহমি শেষের দিকে হাতমেরে ক্লান্ত হয়ে যাওয়া যে আধাটাকলু ভাইটিকে দেখালে সে ও ছিলো। সবগুলিকে নেড়ে ভর্তা বানাও ভাই। অপেক্ষায় রইলাম,1,entertainment
"এক দিন কিস,পরে ভোদা চাডা পরে পুটকি মাইরা হাগা বন্ধ করে দেয়া।।ভালোই।।ওরে আমার ধোন চুষতে দেয়া দরকার খানকি মাগি",1,entertainment
আসলে প্রভা একটা মাগির 30 মিনিটের ভিডিও আছে,1,entertainment
"ছাগলের দল আরবি উচ্চারণ ও করতে পারে না ... রে, যে, খেহবে না... সঠিক উচ্চারন হবের, জ , খ",1,entertainment
এই মদার চোদ কে এই সালারে মিডিয়ার সব কিছু  থেকে বয়কট করার জোর দাবি জানচ্ছি😡😡😡,1,entertainment
এই ধোনের বিচারকদের বাদ দেন এই ভোদার বিচারক এর কারনে কেউ আর কোন রিয়ালিটি শোতে অডিশনে যাবে না।,1,entertainment
"কোন মাদারচোদ পরিচালক, মাথা মুন্ডু কিছু নাই,",1,entertainment
এরা বাল ছেরা চুদি বিচারক,1,entertainment
মাসুদ রানার মারে মারে আমি চুদি যদিও কখনো মাসুদ রানা আসে আমি উ আমার বন্ধু বান্দবদের মানা করবো দেখার জন্যে।,1,entertainment
বোদার মাসুদ রানাকে চাইনা কিন্তু আমার বাংলার ভাইদের অপমান করার দরকার নাই,1,entertainment
পাগল ছাগল বিচারক অনুষ্ঠানে নামে টাকা দানধা বাজি।,1,entertainment
এই গাদার বাচ্চা পরিচালক কি নাটক বানাইচত,1,entertainment
এই জানোয়ার গুলারে নিজের হাতে জুতা মেরে গাল ফাটিয়ে দিতে ইচ্ছে করে ওদের বাবা মা মানুষ বানাতে পারেনি কিভাবে মানুষকে সম্মান করতে হয় সালার জানোয়ার কোথাকার গুলি,1,entertainment
দুধ দুটি ছিড়ে পরে যাচছে বোরকা নিয়ে কথা বলছ মাগি তোর দুধের চিনতা কর,1,entertainment
মাগা মাগিদের কাছে পাইলে জুতা দিয়ে পিটা তাম! ভাই তোদের কাছে একটা পিস্তল আছে থাকলে একটা দেয়!,1,entertainment
"শালী পপি তুই জানার পর ও আমিন খানের সাথে আসলি কেনো,,,,,যে শাকিব তর খেলার সাথি,,,,পাট ক্ষেথে যাবার গালি আইচ্ছ,,,,আসলে তুই অস্টেলিয়ার গাই।",1,entertainment
হিরো আলম এর বউ ন না সানাই পতিতা মান সবাই,1,entertainment
এলিয়েন শুভ কে ময়লা নাঈমের দুধের চিপায় লুকিয়ে রাখা যাবে,1,entertainment
সেইরকম মাগী 🖕,1,entertainment
মাহির পাছা বড় হয়ে গেছে 🤣🤣🤣🤣😂😂😂🤣🤣🤭🤭🤣😂,1,entertainment
বালের নায়েকা তুই তুই যদি নায়েকা হয়ছ দেশের সব নায়েকারা দেশ চেরে পালাইবে,1,entertainment
খানকি মাগি চেকাপ করালেও এত টাকা লাগে না লাক টাকা তুর ভুদা বেচে এনেছিস,1,entertainment
বুড়োর কাছে তো ভাজিন হব। বুড়ায় ভাজিনের কি বুঝবে সৃজিত কে কুকুরের সাথেওভাজিনবলবে। সালা কুকুরের ছেও খারাপ।,1,entertainment
"বাসায় কি একা? সেক্স করতে মন চায় ? তুমি কি চাও কেউ এসে তোমার ভোদা চুষে দিয়ে যাক? বিধবা, বিপত্নিক, তালাকপ্রাপ্ত, গৃহিনী, ছাত্রী, আবিবাহিতা, স্বামী বিদেশে, বাচ্চা হয় না? আপু ভাবী আন্টি তোমরা যারা সেক্স এর জ্বালায় ভূগছো? সোনালী সময় নষ্ট না করে ফোন কর 01971-129034।",1,entertainment
তাদের কে জুদা মারা দরকার তারের কে জুদি হালার ঘরে হালা।,1,entertainment
বেসার পুলা মাগি,1,entertainment
হট সেক্সী সুন্দরী মেয়ে চাই চোদাচুদির জন্যা আমি সব বয়সের মেয়ে বা মহিলাকে চুদি কোনো সমস্যা নাই সব কিছু ১০০% গোপনে করবো তো এখনি কল দাও,1,entertainment
বেশ্যা মাগি তুই দেশের জন্য কি করবে খানকি,1,entertainment
ফাজলামি চোদানোর আর জাইগা পাই না অবশ্যই ফাজলামি করার জাইগা শুধু মাত্র আমাদের দেশ এ অন্য দেশে করলে পুটকি মারা দিবে,1,entertainment
ও একন মাগি হয়ে গেসে,1,entertainment
এখানে যে দুইটা মাগি আছে ঐ দুই টারে ডিসি সাবের কাছে পাঠিয়েদেন জামালপোর,1,entertainment
বিচারক গো লো জুতা দিয়ে থাপর মারার কাম,1,entertainment
নিজে কি মনে করেন। সালা পাগল,1,entertainment
যে সব ইউটিউবার এই সব বেশ্যা পতিতা কে নিয়ে কিছু ভিউস এট জন্য ইন্টারভিউ নামে বেশ্যার পতিতার দালালী করে তারের কে আনসাবসক্রাইব সবাই ধন্যবাদ,1,entertainment
ভাইরে বাংলা ছবি এখন আর কেউ দেখে না অজথা এই বালডি বাছাই না কইরা চাইনা সিনেমা গুলো ডাবিং কর। তোদের ধান্দা বাচবো😑,1,entertainment
দাড়ীওয়ালা কুত্তার বাচ্ছা কোন রেল সষ্টেশনে জন্ম নিছে জানার খুব দরকার,1,entertainment
পাগল পরিচালক,1,entertainment
শালী এটা কি করলো বাংলাদেশের বদনাম,1,entertainment
বিচারক নামে যা মাগি আর মোদারচোদ।বসলো ওই গুলাকে জুতা মরা দরকার,1,entertainment
মা বাবা যেমন সন্তান ও তেমন ওর মা বেশ্যামাগি ছিলেন আর ওর বাবা বেশ্যামাগিদের দালাল ছিলেন,1,entertainment
মাদারচোদেরা হাউয়ার ইন্টারভিউ নিতে চে😡😡😡,1,entertainment
কুত্তার বাচ্ছাদের জাজ বানাইছে কোন সালায়,1,entertainment
এই রকম জুদি মেয়েদের পটিয়ে খাও জেতো তা হলে ছেলেরা লাকি হইতো,1,entertainment
দড়িওয়ালা মদারচুদ কি মাদারচুদের ছাও,1,entertainment
মেয়ে দুইটার পাছা আমার ভালো লেগেছে,1,entertainment
তর ফেমেলির সব বেস্যা না হয় তুও এত বড় মাগি হলি কি করে।,1,entertainment
রাক্ষস মহিলা এমপি হতে হলে ছেলেদের কাছে হোগামারা দিতে হবে,1,entertainment
তারে চোদোচোদি মোবীতে পাটাতে হবে ৷,1,entertainment
"আসলেই সত্যি কথা বলিতে সৃজিত মিথিলাকে গুদ দিয়ে ঢুকায় নি সৃজিত মিথিলাকে পুটকি মেরেছে তাই সৃজিত মনে করছে যে আমাদের জাতীয় ভাবি মিথিলা এখনও ভার্জিন।। কারন পুটকির ছেদা অতিশয় টাইট থাকে,,,, তাই কলকাতার আবালের বাচ্চাটা বুঝতেই পারলো নহে ।।",1,entertainment
আচোদার ঘরে মাষ্টার,1,entertainment
সানিতার তো অনেক বড় বড় দুধ চাপা টা একটু বেশী হইছে,1,entertainment
কী বলা যায় তাকে পতিতা ব্যাশা খাংকী নায়িকা নাকী চুতমারানী,1,entertainment
কেহ দেহ ব্যবসা করে পতিতালয়ে কেহ ফ্লাটে কেহ গোপনে কেহ মন্চে কেহ সিনেমায় কেহ কল গার্ল কহ ফাশান শোতে কেহ ভিডিও কলে কেহ,1,entertainment
বিচারক গুলা অাসলেই মাদারচোদ অজ্ঞ ওরা মনে হয় হিরো হয়েই জন্ম নিয়েছে শালা শালিরা,1,entertainment
যারা যারা এই সপ্ন খানকির ছেলে ভক্ত আছস তরা তোদের আম্মুকে চুদস বেইশ্যা পুলা। এই বেয়াদবের চ্যানেল কর। সে একটা বেইশ্যার ছেলে। রিপোর্ট করেন আপনারা এই চ্যানেলে যদি আপনার মা বাবা চরিত্রবান সৎ হয়ে থাকে।,1,entertainment
আবালের মাইরে বাপ এ কেমন জাজড রে ভাই,1,entertainment
ফারিয়ার সাথে যেটা বসছে ওটা আসলেই মাদারচোদ,1,entertainment
খানকি তুই দুধ বড় করিয়েছিস ভালো কথা। কিন্তু জাতির সামনে প্রকাশ করলি কেন মাগি কোথাকার আমরা ছেলেরাও তো আমাদের সোনা বড় করাই কিন্তু জাতির সামনে তো প্রকাশ করিনা। মাগী,1,entertainment
ওই কুত্তার বাচ্চা জোরে দে...😁😁😁😁 জিনিয়াস রা বুঝবে....,1,entertainment
আসলে বিচারক গুলো বেজন্মা,1,entertainment
হাবিব তোকে চোদবে মাংগের বেটি। লাখ খরচ না করে চোদা দিলে তার চেয়ে বড় হত তোর দুধ,1,entertainment
মোমো এবং ফারিয়া দুইটাই উন্নত মানের দুধেল গাভী ছাড়া আর কিছুই নয়,1,entertainment
জাজ গুলাই লেবেলে নাই তারা আবার অন্য জনকে জাজ করে । এর জাজ দের মত হইতে চায় শালার পুত সব গুলা নকলবাজ।,1,entertainment
জাহান্মামের কিট,1,entertainment
খানকিমাগির পুলা মন চাচ্ছে তোদের মা বোনরে চুদে কেউরাতলা পাঠায় দেই আর খানকি গোলারে চুদে চুদে বেলতলাতে পাঠায়,1,entertainment
মম এর সোনা একের লাল মম এর সোনার কিচু বাহির করা দরকার মিডিয়া থেকে বাহির করে দেয়ার দরকার,1,entertainment
খানকি। দুধ বড় করছোস। এখন তোর বোদাডা ও বড় বানা। পরে ভাল দেখে একটা ঘুড়া কিন। তইলেই তোর কাম হবে।,1,entertainment
খানকি এই সব বাদ দে নামাজ পর,1,entertainment
ও হচ্চে একটা এক নাম্বার খানকি। so that.s all......,1,entertainment
ওই শালা দারিয়ালার নাম কি কেউ দয়াকরে যানাবেন। শালা বাইনচোদ।,1,entertainment
এই খানকির পোলাগো বিচারক বানাইছে কোন মাদার চুদ,1,entertainment
মম ও পারিয়া তোরা কোন হেড়া চেহারা লই বসে আচত আর শালার বেটারা তোদের কি বালের চেহারা শালা কুল্ঙার বাচ্চারা,1,entertainment
বালের লিখক হেয় আর সুনার বিচারক ভুদার বিচারিকা,1,entertainment
সানিতা আর সানিলিয়ন এর মাঝে কোন পার্থক্য নাই আস্তা একটা মাগি হবে।,1,entertainment
চ্যানেল আই মাদারচোদ 😡আর বিচারক রা তো জারজ সন্তান তোদের কে কাছে পাইলে হাতির হোল দিয়ে চুদাই নিতাম,1,entertainment
মাসুদ রানা শোটারে বিচারকরা মাদারচোদ রানা বানাই দিসে।🤧,1,entertainment
তর মারে চুদে হালার পুত<br />এই সব ফালতু কতা,1,entertainment
কুত্তার বাচ্চা এই ধরনের ভিডিও কেন বানাস,1,entertainment
"কিছু বলার বাসা নাই ,কিছু কিছু কুত্তার বাচ্ছা জন্য ও এমন হয়, এক জন্য বলছো কেনো তারা কথা বলি কেনো ? হে ভাই আমরা ছেলে কেনোতাদের সুন্দর দেখা সুখে পথ দেখাই ,যেম একটা মেয়ে কে তার বাবা মা কিয়ে দে তো সুখ জন্য ভালো থাকার জন্য কিন্তু কিছু কুত্তার বাচ্ছা নেসার জন্য বিক্রি করে দেই ,আবার নিজে সব কিছু সেষ করে পরে বিয়া না করে বিক্রিকরে দেইদুসু এটা বলে হবে না,তারাখারাপ, ,কোনো কোনো কারন এমনা হয়ছে, আচ তো আত আমরা ওগাড়ি নিজে পরে মরে যেতে পারি তাই কি গাড়ি ওলাদাই না কারন আমি দেখা যাই নি, আসো সবাই নিজে নিজে সব কিছু ঠিক করি পারলে, নিজে তাদের টাকা দিয়ে এনে একটা সুখে ঠিকনা দেন দেখন তারা কতো খুশি হয়, ওপর ওলা আপনার জন্য খুশি হবে, আমার কথা বলে হলে খমা চখে দেখবেন সরি? /////",1,entertainment
পরিচালকের মায়েরে কুত্তা দিয়া চুদি,1,entertainment
তোর মার হেডা আবাল,1,entertainment
বাংলার শ্রেষ্ঠ মাগি সানাই,1,entertainment
যারা জাজ হিসেবে আছে তারা কোন কোন মুভি করেছে জাতি জানতে চায় আবালসুদা জাজ এগুলোকে জাজ যারা বানাইছে তারা আরো বড় আবাল,1,entertainment
সব কয়টি মাদারী চুদ,1,entertainment
আমি ভারত থেকে বলছি আসলে এই বিচারকদের জন্ম হয়েছে বেলুন দুর্ঘটনায়। যদি সঠিক বাবা মায়ের সন্তান হইতো অন্ততপক্ষে এদের সাথে ভালো আচরণ করতে পারত।।সবগুলো জারজ।,1,entertainment
ব্যাশা দের বাবু হয় বর হয় না,1,entertainment
রুমানা একটা মাগি তাই এমন করলো,1,entertainment
মাদারচোদ দের আচরণ কুত্তার চেয়েও অধম😠😠,1,entertainment
শালি একটা খানকি মাগি,1,entertainment
সালারা আমার বাল বানাও,1,entertainment
আকাটা ধন চুষতে হবে মিথিলার,1,entertainment
বাংলাদেশের সব নাইকারা পতিতা।,1,entertainment
খগেনসাহা। আবাল খান,1,entertainment
সালা গ্রামের ডোম গুলো সব আইছে বিচারক হইয়া।,1,entertainment
প্রভা কে আমার বালো লাগে কিন্তু তারচে বেসি তার দুধুগুলা,1,entertainment
ইফতেখার আহমেদ ফাহমি খানকির পোলার মারে কুত্তা দিয়া চুদাই,1,entertainment
ভিডিওটি যারা দেখেছেন তারাতারি বাল ফালান মাল ফালান গোসলে যান জলদি,1,entertainment
এই বাংলার মাটিতে কুত্তার বাচ্চাদের কিভাবে এত সাহস হয় যে আমার দেশের সোনার ছেলেদের কে এভাবে অপমান করতে,1,entertainment
একদম খাটি মাগি।,1,entertainment
নায়িকা দেখিয়া হাত মারবি নাকি।বুকা চুদার দল।কমেডিয়ান ২ ছেলে থাকতে মেয়ের কি দরকার।,1,entertainment
ভাল রোস্ট হল বালের মাসুদ রানা,1,entertainment
কত বড় বেশ্যা হলে এসব করতে পারে একে গন রেফ করে মেরে ফেলে উচিত বাংগালি জাতির কলংকো সারা নারীর বদনাম করার জন্য এই একজন বেশ্যায় কাফি জারোজ ফ্যামেলির জারোজ পতিতা খানকি কুওার বাচ্চাদের কারনে দেশের বারোটা বাচছে মাদারির বাচ্চা এখন পরনো ভিডিও বানা,1,entertainment
দেশটির হোলোকি এই সব বাজে খানিকদের নিয়ে মাতামাতি,1,entertainment
বদের বাচ্চা এসব বন্ধ কর,1,entertainment
পাগল ছাগল হইয়া গেছে বিচারক,1,entertainment
সাকিবের ধোন কাইটা ফালাই দেন,1,entertainment
বাল দড়ি অলা আবাল সুদাডার নাম কি হেতে একটা বড় মাপের মাদার ছুদ।,1,entertainment
শবনম ফারিয়া একটা পতিতার তলায় থেকে এসেছে আর ওর সাথে একটা আছে খাটাশ এগুলো খাটাশ এইরকম আমরা কোনদিন দেখিনি,1,entertainment
আর মত মাগির ছবি মানুষ সে দেখবে,1,entertainment
পরিচালক নাটকের মত পাগল এইটা কি নাটক হলো। সময়র দাম নাই ।তোরা শালা কুকুর।,1,entertainment
চেকাপের সময় তকে চুদে চেক করেছে,1,entertainment
সব চেয়ে খারাপ লাগলো অই কালো ছেলেটার কমেন্ট শুনে।এদের কে গালি দিলে ও গালির অপমান হবে।সুওরের বাচ্চা রা।কোন মাষ্টারে তদের শিক্ষা দান করছে।জানতে বড় ইচ্চে হয়।,1,entertainment
এই সব মাগিদের ইনটারভিউ কোন আবালে রা যে নেয় এদের টিভিতে না দেখিয়ে অন্য কিছু দেখান,1,entertainment
চুদদা মাইরালা মাগিরে ।,1,entertainment
কবিতা মাসূদ রানা সে হলো কুকুরের ছানা অফিসে বসাইছে আবালের পনা সালামের উত্তর নাই তাদের জানা অষ্টলীয়ার গাইকে তোঁ সবারী চেনা নাটকে দেখায় ধূদের কনা !!,1,entertainment
এরা নম্বর ছাগলের বাচ্চা। সবগুলো নেশাখোর ।,1,entertainment
বিচারক গুলা পুরাই কুত্তার বাচ্চা,1,entertainment
সানাই তই খানকিগিরি করবি আর তোকে সবাই ভল বলবে এটাকেমন করে হয়।,1,entertainment
বিচারক সব কয়টা কুত্তার বাচ্চা কুত্তার জর্ম্না তা না হলে এমন করে কথা বলতো না আরেকটা জংলী শালা মাদার চোদ নিজের দিকে তাকা আগে জংলী,1,entertainment
দাড়ি ওলা মাদার কে চোদ,1,entertainment
হিরচি গুলো এখানে জমা হইছে মম চুতমারানি কে ভালো ভাবতাম যে যার মত সবাইকে অপমান করতেছে,1,entertainment
জয় একটা কুত্তার বাচ্চা,1,entertainment
মাসুদ রানা তো শয়তানের পয়দার হে কি বিচারক মাদার চুধ,1,entertainment
আপনারা জানেন না। এই মেয়েটা আসলে ও পতিতা। শুধু পতিতা না। এক নাম্বার খানকি।টাকার জন্য সব করতে পারে।আমি তাকে চিনি,1,entertainment
কুত্তার মতো তোমাদের শুনা অাটকাইয়া যাবো তখন মজা বুঝবা।,1,entertainment
নিজেদের কে বানরের মত লাগছে সব পাগলের দল।,1,entertainment
জে লেকছে তার মাথা খারাপ গানজা কুর । হালার গড়ের হালার ।,1,entertainment
তোদের বোদায় কিড়া পরবে তোরা মোছল মানের দাড়ি নিয়া মোসকারি চোদাশ নটির মাগি আর খাংকির পুলারা তোদের বোদায় পেট টুল ডাইলা আগুন দেওয়ান দরকার ছিল,1,entertainment
দুরু গরুর ফুয়াইন সেলেটি মাত ফারস না তে নাটক বানানাস কেনে,1,entertainment
কত গুলো বিচারক নামে গরু বসে আছে।,1,entertainment
বিচারক গুলারে থাপরায়া কানের পর্দা ফাটানো উচিত ৷ মাইয়া গুলার নিচে তো ফাটাই অন্য জানোয়ার গুলারো ফাটানো উচিত ৷ দারিওয়ালা ছাগল আর বুবনাম ফারিয়া কে স্পেশাল থাপ্পর দেয়া উচিত,1,entertainment
চ্যানেল আইয়ের মত গুরুত্বপূর্ন একটা জায়গায় অস্ট্রেলিয়ান গাভী প্রদর্শনী বেমানান আর এই জঙ্গি গুলা কারা,1,entertainment
এসব সব বড় বড় মাগি,1,entertainment
এই খানকির পুলারারে কে বিচারক বানাইছে!!!বোকাচুদারা,1,entertainment
হেতিরে বাল ছাড়া কেউ হজম করতে পারবেনা। কারন রতনে রথন চেনে কুত্তায় চিনে কুত্তি।,1,entertainment
প্রথমে তোর দুধে মারমু দোন।তারপর ভুদাই মারমু তারপর মুখে মার মু দোন,1,entertainment
ছেলেদের যেভাবে অপমান করছে।।আমি জাজদের চুদি,1,entertainment
শালা জংলি সে নাকি এসেছে বিচারক হতে আবার নাকি সে নাটক নির্মাতা তাকে জুতা মারা উচিত্ জংলি জানোয়ার কে বিচারক বানিয়েছে,1,entertainment
এই শাউয়া দুইটা সৌভিক আর জাকি এই হ্যাডার পোলা গোরে কেন এই ধরনের নাটকে নেই আল্লাহ জানে,1,entertainment
অনন্ত অভিনয়ের বাল ও পারেনা,1,entertainment
মুসলিম মাগি😜😜,1,entertainment
আরে মাদার চুদের ছবি কোনে আগা মাতা নাই,1,entertainment
বিচারক কের মাই রে চুদি,1,entertainment
মাদার চুদের বাচ্চারা মানুষকে সম্মান করতে শিখ,1,entertainment
খাংকির পোলারে কুত্তা দিয়া চোদা,1,entertainment
বিচারকরা তো ভুদায়,1,entertainment
প্রভা মাগি চােদার পাগল আমি নেগেটে সব দেখছি শালি একটা মাল,1,entertainment
এবারো বাংলা মাতাবে হালা একটা মাধারী,1,entertainment
মাসুদরানাকে খুজতেছে না বালাখানার সহকর্মী কে খুজতেছে বিচারকরা একটা বালা খানা !!,1,entertainment
খানকির বাচ্চা খানকি তুরে কি কমু ক্য বেশ্যা মাগির মেয়ে তুর দুদ বড় করে জাতির মা বোনদের অপমান করেছিস 😡😡😡আমি মেয়ে হয়ে বলছি তুরে তুর দুদ আমার কাছে নিয়ে আসতি আমিই টিপে বড় করে দিতাম😠😠 ভুস্কির ঘরে ভুস্কি তুর দুদের মধ্যে গরম সিক দিয়ে ছ্যাকা দেওয়া দরকার ছিলো😠😠 মাগির ঘরে মাগি 😡😠😠😠😡,1,entertainment
এই শালায় রে মেকাপ করার পরও চুরের মত দেখা যা মিডিয়া পাগল হয়ে গেছে বস্তি থেকে লোকজন দরে এনে নাটক বানায় দেশে স্মাট ছেলে মেয়ে কম আছে,1,entertainment
বিচারক গুলা কে জুতা দিয়ে পিটা উচিৎ মাদার চুদ,1,entertainment
এই ধরনের মাগী গুলিকে। কাঁটা ওয়ালা গাচ দিয়ার। দরকার,1,entertainment
মাগীর পোলারা মাগী বাজ আর মেয়ে গুলু ও মাগীর মত চেহারা,1,entertainment
মাদারচোদেরা হাসান কই,1,entertainment
মাগি,1,entertainment
শায়লা একটা কুত্তার বাচ্চা।,1,entertainment
বালের নায়ক আমিন খান।আইসা মুভিটা ই নস্ট করল,1,entertainment
কোন পতিতালয়ে ছিলো যে তার বুক বড় করতে হবে জন্মগত ভাবেই ত্রুটি আছে না হলে এমন ধারনা কেন হল যে বুক বড় হলেই তাকে মানুষ স্পেশালিষ্ট ভাবে দেখছে বেয়াদব,1,entertainment
তোদের মতো ছাগল দিয়া এই বিচার হবে না,1,entertainment
এই বিচারক কে তার বাবা শুদ্ধভাবে জন্ম দেয়নি,1,entertainment
বাংলাদেশি বালকামা এই জজদের জন্য আজকে আমাদের বাংলার হিরো সাইমন ছাড়া আর কেউ নেই এই শালা কুত্তার বাচ্চাদের জুতাপেটা করা হোক কে কে আমার সাথে আছেন হাত তুলুন 🖐️,1,entertainment
"বরর্তমানে নায়ক গুলো,,, হালারপো",1,entertainment
দুধ ধরে চিপ মারবো! 🤣,1,entertainment
সোনা সিলাই লাইয় করছে ।এই জন্যেই ভার্জিন।,1,entertainment
কুত্তা বাচ্চা ফালতু নাটক,1,entertainment
কিছু কিছু মেয়ে আছে অতিরিক্ত বাল পাকনামির কারনেও এই হাল হয় ! কথায় আছেসুখে থাকতে ভুতে খিলায়|,1,entertainment
মেয়েদের মানসম্মান শেষ করে দিলো মাগি।,1,entertainment
এসব বাস্টার্ড মেয়েদের কে নিয়ে নিউজ না করে ভালো কোনো বিষয় নিয়ে নিউজ করেন,1,entertainment
মমো তরে কুওা দিয়া চুদাইলে তুই বিচারক হতে পারবি।,1,entertainment
এদের সামনে এদের মা কে চুদতে হবে আর শবনম ফারিয়া যে সেক্সি সাওয়াতে ভদা তে মাল দিতে হবে ওকে চুদতে মজা হবে৷৷,1,entertainment
এ মাগির পোলা রা ছবি চলে না,1,entertainment
না?? তোর মায়েরে তুই চোদ খানকির পোলা। তোর পুটকির মধ্যে পদ্মা সেতুর পিলার ঢুকাব বেশ্যা মাগির ছোল। তোর টেংরি কেটে ভোদা বানাবো। আর তোর ভোদা দিয়ে ওই মরা হোল ঢুকাব বাইনচোদ। তোর বেফোমিটরে কুত্তা দিয়ে চোদাই সাউয়ার বেটা। যারা যারা একমত লাইক মারো।,1,entertainment
শালা বাংলাদেশের পাগল এর অভাব নাই,1,entertainment
বালের পরিচালক,1,entertainment
সাওয়া চুদা বিচারক,1,entertainment
খানকি মাগি তাহসান ভাই কে রেখে তুই বুইরাটার কাছে কি দেখছোত বুইরাটা তো তোকে টিপ দিতে ও পারবে না,1,entertainment
সাউয়া মিডিয়া😂😂😂😂😂😂😂😂😂😂😂,1,entertainment
শাউয়া চুদি কি কয়,1,entertainment
ভাই তোর গান শুনে আমার ডাইরিয়া হোয়ে গেছে 🤢🤢 তুই কার কাছ থেকে গান শিকছচ ক একবার ?? তুই বাঙ্গালিরে অপমান করছচ😤😤কুত্তার মতো চিল্লালেই কি গান হয় গান হলো মোনকে আকৃষ্ট করার জিনিষ তোর এডা কি??😡😡,1,entertainment
সব গুলো খানকি।। এই মাগি গুলো কে মিডিয়ার সামনে আনে কে।।,1,entertainment
ওই আবুল মার্কা হিরোকে ঢাকতেই মনে হয় আবালচোদা ডিরেক্টর স্টিল ছবি দিয়া গানটা রিলিজ দিছে। এইভাবে হিরুকে ঢাইকা ছবি রিলিজ দিবো..... হাহা হা ....... সেই ছবি আবার হিট হইবো???? হা হা হা,1,entertainment
এই সালায় একটা পাগল ছাগল নায়েক নাইকাটা ঠিক আছে,1,entertainment
ডনের মারে চুদি,1,entertainment
"কুকুরের বাচ্চা ধর্ম নিয়া নাটক করছ কেন, মাদারসুত খানকি মাগীর পোলা।",1,entertainment
এ মাগিটারে একবার চুদিচি এ মাগিটার দুদ অনেক ভড়,1,entertainment
দাড়িওয়ালা শালা আস্তো একটা বেয়াদব। শোওরের মত ব্যবহার। আর মমো আর ফারিয়াকে আমার ভাল লাগত কিন্তু তাদের ব্যাবহার ও খারাপ। মূর্খের গোষ্ঠী। আমার মনে হয় বিচারকরা অশিক্ষিত বর্বর নিম্নশ্রেণী বস্তি থেকে উঠে আসা নর্দমার কীট।,1,entertainment
বিচারক বানায়ছে কেডা এইগুলারে জীবনে অনেক আবাল দেকছি এমন আবাল দেখি নাই,1,entertainment
এই মাগীকে।জুতা দিয়া পাঠানোর দরকার নিলজ্জা শালী,1,entertainment
বালের নায়ক... বালের ছবি... বালের পরিচালক... বালের অভিনয়..,1,entertainment
এই সালির মারে চুদাও,1,entertainment
এই সমস্ত মাগির এরকম ই হওয়া উচিত,1,entertainment
সানাই দুধ রপ্তানি করে পছুর বৈদেশিক মুদ্রা অজন করতে পারবে,1,entertainment
শবনম ফারিয়া একটা আর ওর পাশের টা ওই খানকির পোলার নাম কি মাদারচোদ একটা,1,entertainment
কুত্তার বাচ্চা মতন ব্যবহার,1,entertainment
কুত্তার বাচ্চা সব গুলা।ওদের তো দেখা যায় কুত্ততার মত।নিজের যোগ্যতা বিচার না করে আসছে অন্যের যোগ্যতা বিচার করতে।পেলে জুতা দিয়ে পিটাই দিতাম সালাগো।ফালতুরা,1,entertainment
এইসব খানকি দের কারনেই দেশের আজ এই অবস্থা যেমন শিল্পী তেমন উপ স্থাপক টাকার বিনিময়ে নগ্ন হওয়ার কথা বলে হায়রে অনুষ্টান,1,entertainment
মাদার টোস্ট বিচারক গুলো,1,entertainment
কুত্তার বাচ্চা হিরনীন খোর দের বিচারক কে বানাইছে সে চুতিয়া,1,entertainment
তরে আমি একবার চুদতে চাই,1,entertainment
জয় বাই আপনার সব সো আমি দেখি আপনি এরকম একটা পতিতার ইন্টারভিউ নিচ্ছেন,1,entertainment
এ ই দুই হেন্ডা মারানি রে স্টেজে পালাই সবার সামনে চোদার দরকার ছিল।আর যে দুই আবাল আছে আমি হইলে তো স্টেজে গালের মধ্যে চোড় বসাই দিতাম সবার সামনে। সবচেয়ে বড়ো কথা হলো যে হেন্ডা মারানি গোরে দেখি আর বিছা খাড়াই গেছে এখোনি আবাল এ র মারে চুদি মাগি গোরে স্টেজে চুদি,1,entertainment
পরি পরি তুই সবাই কে ভাল করে চুদতে দিবি রে,1,entertainment
মোমো তরে তরে আমি বিনা পয়সায় আমি চুদুম না আর যে দুই মাদার চুদে বিচারক হয়েছে তাদের থেকে বাজারের কুত্তাও সুন্দর,1,entertainment
কুত্তার বাচ্চা ডন তরে সামনে পাইলে কুত্তার মত পেটাবো ।<br />বগুড়ায় জেলা কলঙ্কিত খলনায়ক আশরাফুল ইসলাম ডন জাতীয় কুলাঙ্গার জন্মটা হয়েছে সমাজের নিকৃষ্ট দৃশ্যপটে এই ঘাতক নিমক হারাম নায়ক সালমান শাহ হত্যাকান্ডের সাথে জড়িত । এই কুত্তার বাচ্চা কে দেখলে গা জ্বলে উঠে ...<br />শুয়োরের বাচ্চা কুলাঙ্গার জারজ খানকির পোলা ডন ।,1,entertainment
এইগুলার মতো বস্তি বিচারক হলে বালের নায়ক বের হবে🖕কারো সাথে কী ভাবে ব্যবহার করতে জানে না এরা কি বালের মাসুদ রানা বের করবে,1,entertainment
সালি একটা মানসিগরুগি,1,entertainment
ভুদাই,1,entertainment
এই মাগিই রে ঢাকা তেন সরান খান কিই কুতার বাচচা,1,entertainment
এই খানকির ছেলেকে এখন পর্যন্ত কেউ মারে নাই আমি ঐ খানে থাকলেতো খানকির ছেলেকে না মেরে বের হতাম না 😡😡😡😡😡🤬🤬🤬🤬😡,1,entertainment
শালা চাগলে দল কি বলবো,1,entertainment
গানটা এতদিন শুনতাম কিন্তু জানতাম না এইটা আবাল চুদার মুভির গান<br />হৃদয় খান এই আবার চুদার মুভিতে গানটা দিয়ে ভুল করছে<br />গানটা চুদে দিয়েছে,1,entertainment
বিচারক রে জুতা মার কথা ঠিকমতো বলতে পারে না প্রতিযোগীর সাথে,1,entertainment
চ্যানেল আইয়ের মায়েরেচুদি। বালের জাজ নিয়েছো। আমরা চিনি না। ভাব নেয় এমন যে সেপৃথিবীর সুপার স্টার আবালের দল,1,entertainment
বিচারক না মাদারচুদ,1,entertainment
ভাই আপু কয়বার চুদে পাগিয়ে পেলছেন,1,entertainment
মাগী রে চুইদা,1,entertainment
আমাদের ব্রাম্মনবাড়িয়ার মতো ভাষা হা হা হা চুতমারানির মাগি,1,entertainment
একটি ছেলে বিয়ে করবে কিন্তু তার কথা হলো ভার্জিন মেয়ে হতে হবে তাই যেখানেই মেয়ে দেখতে যায় সেখানেই তার কথা থাকে মেয়ের সাথে সে একান্ত ভাবে কথা বলতে হবে কিন্তু যখনই মেয়ের সাথে কথা হয় তখনই বিয়ে ভেংঙ্গে যায় যাই হোক এভাবে অনেক মে দেখার পরে এক যায়গায় মেয়ে দেখতে গেল তার পরে মেয়ে টিকি ছেলেটি একটি রুমে নিয়ে ছেলেটির প্যান্টের চেইন খুলে দেখাল আর বলল তুমি বলতে পার আমার এটা কি মেয়েটি চালাক ছিল এবং সে আগের মেয়েদের কাছ থেকে একথা যেনে ছে যে তাদের সাথে কি কারনে বিয়ে হয় নাই তাই সে বলল হ্যা এবার ছেলেটি জিগ্গেস করল তাহলে বলতো এটা কি? মেয়ে টি লাজুক ভাবে বলল ওটা তো নুনু।এবার ছেলেটি খুশি হল কারন আগের মেয়েরা কেহ বলছিল ভারা কেহ বলছিল লিংগ কেহ ধোন তাই ছেলেটি বুঝ ছিল যে এরা যখন চিনেছে তাহলে তারা ভার্জিন না।এবার বিয়ে হল বাসর রাতে ছেলেটি তার বউয়ের কাছে গেল কিন্তু গিয়ে দেখে সেত সানিলায়ন এবার ছেলেত অভাক সে তার বউকে জিগ্গাস করল কিরে তোমার পালাকি তুমিতো সেদিন আমার ওটা দেখে নুনু বললা আমিকো মনে করেছিলা যে তুমি কখনোই বড় মানসেরতা দেখনাই তাই নুনু বলছ আর তুমি সতি আছ।এবার মেয়েটি হেসে উত্তর দিল আেে বোকা এতদিন আমি যাদেরতা দেখেছি তাদের কার তুলনায় তোমার তা নুনু।তাই সৃজিত দাদা এতোদিন যাদের তা দেখেছে তাদের তুলনায় মিথিলা ভার্জিন।😁😁😁😁😁😁😐😐😂😂😂😂😂😂😂😂😂,1,entertainment
নায়িকারে তো হিজরার মত দেখা যায়<br />পুরাই ময়দা,1,entertainment
বেটকাইয়া লাভ নাই ওরা হইল গরুর দালাল।,1,entertainment
আমি বুঝতে পারিনা “পাহাড়ি দুধ ওয়ালা দিদি হাটে কী ভাবে,1,entertainment
এইসব বালচাল গ্রুমিং আর র‍্যম্প কিছুই কাজে লাগবে না যদি ভাল অভিনয় না পারে। তাই তাদের অভিনয়ের দক্ষতা বারবার নেয়া উচিত।,1,entertainment
ফালতু থু থু দিলাম তুর মুখে,1,entertainment
আমি ঐখানে থাকলে ওই শালা মাগির উপর স্যান্ডেল চর মারতাম,1,entertainment
সব চোতমারা মারকা শো,1,entertainment
বুরি পুনিমার ভোদা চাটামু কুকুর দিয়া,1,entertainment
আমাদের এই দাঁড়ি ভরা বিচারক ভেড়ি কুল! সে প্রাপ্ত বয়ষ্ক মাদি কে সারা মাস চুদলেও প্রেগ্নেন্ট হয়ার ভয় থাকে না মাদারফাকিং কুল!,1,entertainment
এ খানকির বাচ্চারে কি দেখে ক্যামেরা সামনে নেয় এরে চুদে কই,1,entertainment
এই বেশ্যামাগির লজ্জা বলতে কিছুই নেই মাগিরে ধইরা দুধ দুইটা ব্লেড দিয়া কুচিকুচি কইরা কাইটা কাচা মরিচ বাইটা ডোলে দিলেই আর এই ধরনের কথা বলবেনা,1,entertainment
মাদাচুত মাগির পুলা,1,entertainment
আল্লাহর গজব যে কত প্রকার ও কি কি এইটা মনে হয়ে এই খানকি মাগী জানে না হেইর ব্রেস্টের উপর আল্লাহর গজব খুব তারাতারি পরবে ইনশাআল্লাহ আপনারা দেখে নিয়েন। এমন পচনের সৃষ্টি হবে হেইর ব্রেস্টে যা কিনা হেই নিচতলা চিরদিনের জন্য ভাড়া দিয়া বা ঘন্টা চুদায়াও যে টাকা পাবে এই টাকা দিয়ে এই পঁচনের ঔষধ কেনা শেষ হবে না।। উপরে এক আল্লাহ্ আছে আল্লাহ্ ও আল্লাহ্ এই খানকির উপর তুমি গজব নাজিল কর যাতে আমি এই গজবের আলামত দেইখা মরতে পারি। সমাজকে আল্লাহ্ তুমি রক্ষা কর এইসব বিষাক্ত সাপ থেকে।,1,entertainment
আপনার দুদ ধরে টিপ দেওয়া উচিৎ 😂😂😂,1,entertainment
দুধের বাহার বুদাটা কেমন,1,entertainment
আশ্চর্য আপনি কিভাবে এমন পতিতাককে মডেল বলেন।,1,entertainment
বালের হিরো সব কয়টা বাদর মুখো,1,entertainment
এই মজার টিভির ভুদার পুলাপা৷ হুন বাংলাদেশ এর ইউটিউব টা তুদের জন্যই নস্ট হচ্ছে তুরা শালা লুচ্চা এজন্যই তাহসান ভাইয়া পুন্দাইসে তুদের সব দের জন্যই একটা তাহসানেশন ই এনাফ,1,entertainment
নোয়াখাইল্লা ছাগলচুন্নি কিভাবে বিচারক হয়,1,entertainment
কুক্তার বাচ্চা রা মানুষ তা তো মনে হয় না মানুষ কে বাহির থেকে দেখে অপমান করার অধিকার কে দিচে তোদের কে এই খানে এত গুলি ছেলে আইচে তোদের থাকে হাজার গুন ভালে মানুষকে সম্মান করতে শিখো তাহলে সম্মান পাবে ছরি বাজে কথা বলার জন্য,1,entertainment
তুই যদি তর নিজের মাকে না চুদছ তাহলে আল্লাহর কাছে দায় থাকবি,1,entertainment
"বাল বানাই ছে সালা নকল বাজ, অনেক পিছনে রয়েই গেলা।",1,entertainment
সালে কুত্তার বাচ্চা আর শুয়রের মেয়ে চারটার গাজাখুর আচরণদেখে সবগুলোকে টয়লেট টাংকিতে চুবাতে মন চাচ্চে,1,entertainment
খানকির পোলা জোরে দে 😝😝🤣🤣🤣,1,entertainment
তোদের কি কোন কাম নাই সালার পুত একটা মাগি নিয়ে সামনে আছদ,1,entertainment
আপনারা বালের বিচারক হইছেন আমি যদি ওইখানে থাকতাম তোদেরকে জুতাপিটা করতাম আর ওই যে ওরে চুদে দিতাম,1,entertainment
এই খানকির বাচ্ছাদের বিচারক বানাইছে কে,1,entertainment
মৌসুমি আপু আই লাব ইউ মৌসুমি আপু আর রিতু একটা মাগি,1,entertainment
দুইটাই মাগী,1,entertainment
ভাবছিলাম আমিন খান নায়ক<br />বাংলাদেশ আবাল দিয়া বইরা গেছে।<br />বুঝে-না বাল ও আমিন খানরে দিছে সাইড নায়ক আবাল রে দিছে মেইন নায়ক তোগর ছবি দেখবো বাল<br />আমিন ভাই এই বাল মার্কা ছবি কিসের জন্য করে তাই তো বুঝিনা।<br />টামিল এ ছবি বানায় ৬০ বছরের নায়করা আর আমিন ভাইয়ের তো বয়স ৪৭-৪৮তাহলে সে এই বাল মার্কা ছবি কেনো করে।,1,entertainment
এই বালডারে নিয়া নিউজ না করলে হয়না বাল একটা 😑,1,entertainment
"পরিচারক গানজা খায়ছে,মান্না ভাই আর কই জেসমিন, শালা পুরাই গানজা খায়ছে,,এই কারনে বাংলা মিভি দেখি না",1,entertainment
বিচারক দুইটাকে জুতা দিয়া পিডাইলে জুতার অপমান হবে। আর একটি খানকি মাগি আছে কাষ্টমার বারানোর জন্য দেখায়।,1,entertainment
বানচোদ শালা জাজমেন,1,entertainment
সোনার বিচারক আমি বিচারক দের চুদি,1,entertainment
দোরু ব্যাশ্যা মাগী তরে ঘোরা দেয়া চুদার দরকার,1,entertainment
"শালা বোকা চোদা এইটা কোন নাটক হল, কত গুল বুড়ি চোদা মেয়ে নিয়ে অভিনয় করতে নিয়ে আসল।",1,entertainment
ফাহমি ভাই আপনার দুধ ধরে টিপ মারা উচিত 😂🤣😁,1,entertainment
"পরিচালক হালার পুয়া তুই আগে সিলেট শুদ্দ করে বানান শিখ তার পর নাটক করিছ,,,,,,,,এইটা সিলেটি ভাষা না তর কল্লা",1,entertainment
এই বিচারক গুলার জন্মের ঠিক নাই। বস্তির পোলাপান,1,entertainment
পরিচালক একটা খানকির পোলা,1,entertainment
মিথিলা হলো আন্তজার্তিক পতিতা,1,entertainment
চ্যানেল আই কতৃপক্ষ আপনারা কিছু বলুন।এত মানুষ আপনাদের এই ভুল জাজমেন্ট এর কথা বলছে আর আপনারা নিরবে কেনো মানুষ তার মূল্যবান সময় নস্ট করে এই গাঞ্জাখোরদের গাঞ্জুটি জাজমেন্ট কেনো দেখবে,1,entertainment
ফারিয়া মাগীর নামে কেউ কেইস করে না কেন থার্ড ক্লাস খানকি মাগী।,1,entertainment
ওকে যে বিয়ে করবে আমি বলবো ঐ সালার রুচি খারাপ,1,entertainment
মাদারচোদ জাস্টিস,1,entertainment
সাকিব খান নটি মাগির পোলা,1,entertainment
এতেকিতোরগুদমেলানোরয়েছেযেনিযদা য়েতেদেখবো,1,entertainment
সোনার মাসুদ রানা দেখমুই না,1,entertainment
বিচারক নামে এরা মাদারেচোদ মেয়ে গুলা পতিতা,1,entertainment
গুয়ের পানি দিয়ে মুখ ধুইয়া দিতে হবে,1,entertainment
মাগি তর ধুদ গুলো অনেক বড় তকে ধুদের মাজ খান দিয়ে সোনা ডুকিয়ে ইচ্ছে মত চোদে তর এই বদমাইশি বন্দ করা দরকার,1,entertainment
ইফতিকার ফাহামি সালাই আসল বাইনচোদ কুততার মতো ঘেউঘেউ করছে সালা পুরো শুতে,1,entertainment
মাসুদ রানা কে তিনটা বিচিওয়ালা মানুষ 😒,1,entertainment
বিচারক গুলোরে মায়েরে চুদি যত দেখি তত মনে কয় ওগো মায়েরে চুদি খানকি মাখির পোলারা,1,entertainment
বেয়াদোবের বাচচা বেয়াদব তোরে জুতা দিয়া পিটামু জানোয়ারের বাচচা,1,entertainment
এ দরনের বিচারকদের পাচায় লাথি মারা দরকার যতসব আবাল বাল চাল আইছে বিচারক হইতে। বিচারকদের বলতে চাই এইভাবে মানুষকে অপমান করার অধিকার তোদেরকে কে দিয়েছে ব্যাটা পাইজলাম কোথাকার,1,entertainment
হালার পুতেগো ঘুসদে তায়লে তারা তারি মাসুদ রানা হইতে পারবি😂😂 এইগুলা টাকা খাওয়ার জন্য এইরকম করতেছে। জজ 😘😘😘😘 কাইসার ডায়লগ তোদের না দিলেই নয় হালার পুত 🤣🤣🤣🤣,1,entertainment
ঐ মাগি তুই আমার কাছে আয় চোদা কাকে বলে দেখ তুই ব্রাজিলে আয় তোর সোনার পানি সব বাইর করবো,1,entertainment
এই মাগীর কাহিনি দেখে এখন নিজেকে নিয়ে ই লজ্জা লাগে। আমিও জে একটা মেয়ে বলতে খুব খারাপ লাগে,1,entertainment
"মাগির বুড়ো লান্ড লাগবে,তাইতো কলকাতায় মাগি।",1,entertainment
এই শালা তোর যেই চয়েজ তোর চয়েজ এ গেন্জি ও চুল কাটতে হবে তোর যেই শার্ট আর চুল। শালা বুকা চুদা দুদু খাও।,1,entertainment
"কোন আবালচোদা নায়ক এইটা,,,চিনলাম নাহ😂😂,,,আপনারা কেউ চিনলে একটু পরিচয় দেন,,,",1,entertainment
এই বাইঞ্চোদ দের বিচারক হবার কোন যোগ্যতা ই নাই। যা করছে তাতে গালি দিলেও কম মনে হয়,1,entertainment
বলদের বাচ্ছা পরিচালক হলে এরকম নাটক ই তো তৈরী করবে................হিন্দুরা তো বলদের বাচ্ছা ভূল বলি নাই..........,1,entertainment
বিচারক গুলা গরু ছাগলের ন্যায় !,1,entertainment
ফারিয়াকে যদিও আমি তার বিহেভিয়ার দেখে অনেক কিছু বলেছি। ফারিয়া অনেকটা তোমার থেকে ভালো। আর বোরকার নিচে যাই থাকুক সেটাতো আর দেখা যায় না। যারা বোরকা পড়ে তারা পর্দা করে। তার মানে এটা নয় যে তারা নিজেদের দোষ ঢাকার জন্য বোরকা পড়ে। যদিও কিছু কিছু তোমার মত বেয়াদব মেয়ে নষ্টামি করে বোরকা পড়ে বোরকাকে অস্ত্র হিসেবে ব্যবহার করে। যেমন তুমি এখন শবনম ফারিয়াকে সামনে এনে তুমি ভালো সাজার চেষ্টা করছ। তফাৎ হলো তুমি তোমার দুধ বড় করে সামনে এসে গেছ আর ওরা এখনো সামনে আসতে পারেনি। পর্দাশীল মেয়েরা খারাপ না খারাপ মেয়েরাই পর্দাশীল সেজে নিজেদের দোষ ঢেকে ভালো সাজার চেষ্টা করে।,1,entertainment
আর একজনের সাথে পেম হবার পরে আরেক জনের পেম হয় কিভাবে জতসব পাগলচোদার নাটক,1,entertainment
মাগী নিচ তলা ভারা বলতে কি বুঝাতে চাই জানোস মাগী তর ভুদা বিক্রি করে দুধ বানাইতস ভুদা বিক্রি করে দুধ বর করার কী দরকার ছিল আমাদের মত ছেলেদের কাছে আসতি ফ্রিতে তার চেয়ে বেশী বর করে দিতাম তর ঐ দুধে এখন আর ঐ রকম মজা পাওয়া যাবে না আয় আমার কাছে তর দুধ দুইটা কাইটা ছোট করে তারপর আমরা বর করে দেই ৷,1,entertainment
মম খানকি দারিওয়ালা ওর চোদাচুদির লাং,1,entertainment
আললাহ ওর দুধ দুইটার ওপর ঠাঠা ফেলাও যাতে ও হিজলা হয়ে যায় আর জানি দুধ নাচানাচি না করা পারে,1,entertainment
কুত্তার বাচ্চাদের জাজ বানালে এমনই হয়😠😠,1,entertainment
আপনি কি বললেন আমার সবাই মমো এই খানকি মাগি কে চিনি,1,entertainment
সালারা যা আরও অপমান হও মাছুূদরা হওয়ার জন্য,1,entertainment
জাজগুলো মাগিবাজ। আর মাগি,1,entertainment
বিচারকের মাকে চুদি সালাদের রিস্কা চালানোর যোগ্যতা নাই মাগী গুলারে আনছে বিচারক হিসাবে যে মুসলিম সে কখনো নাটক বা মুভী করেনা জায় সব মাগীগুলা আর ছেলেগুলা জারা আছে এক একটি রিস্কা আলার ছেলে হবার ও যোগ্যতা নাই ভাবতেই অবাগ লাগে এরা আবার বিচারক জতসব খ্যাত থাইকা উইঠা আসছে মাদার চোদেরা তোরাই মাসুদরানা হ আমরা দেখি তোদের চুদাচুদি মিডিয়ায় গেছোস ই তো পরিচালোকের চুদা খেয়ে,1,entertainment
তুইএকটামাগি,1,entertainment
তোর মারে চুদি খানকির পোলা আমি গান করছি তোর কি,1,entertainment
নটির বাচ্চা পরিচালক বেগ্রাউন্ট সাউন্ড কম দিলে কি হতো রে আবাল!?,1,entertainment
"সবাই কমেন্ট দেখে আমার মাথা চুদেনা কি কমু,,,কারন শিশু শিল্প আজ এই অবস্তা কেনো সেটা কি আর বলা লাগে,,,আসলে মাগি মজা বুইজা গেছে তাই এই অবস্তা আরকি",1,entertainment
সানাই তুই জানোয়ারের বাচ্চা একজন।,1,entertainment
আমি মনে করি যারা এইগুলাতে অডিশন দিতে যায় তারাই আসল ভোদাই। এই টুকু কমোন সেন্স নাই তাদের যে তারা এইটা চিন্তা করে না যারা তাদের জর্জ তারাই তো জিবনে অডিশন দিয়া মিডিয়াতে আসে নাই তো তারা কিভাবে অডিশন নিবে অন্য মানুষের। বাংলাদেশের বর্তমান কিছু মিডিয়ার মানুষ হল বোকাচোদা।,1,entertainment
কতগুলা কুত্তা আইনা বিচারকের চেয়ারে বসাইয়া রাকছে,1,entertainment
হালার পুতেরা ভোগলামি করার জায়গা পায়না,1,entertainment
তোর বোনে চুদ্দা শালা,1,entertainment
দূর শালা....😡😡😡😡এত কাটাকুটি করে সিনেমা দিলে ভালো লাগে..??????,1,entertainment
মাগিরে বুড়ি বুড়ি লাগে খানকি মাগি,1,entertainment
আর ফারিয়া এবং মম কে বলছি আপনারাতো পরিচালকের সাথে রাত কাটিয়ে অভিনেত্রী হয়ে গেছে পুরুষরা তো সেটা পারে না ওদেরকে নিয়ে হাসেন কেন কতজন পরিচালক প্রযোজকদের সাথে রাত কাটিয়েছেন তার কোন হিসাব আছে আপনাদের জীবন এমন উত্তরা করে কলা খেয়েছিস খানকি,1,entertainment
আমরা কি হতে চাই না ও মাঝি কে চুদেদিল,1,entertainment
মান্না ভাই সত্যি ওয়ান পিছ ছিলেন।কিন্তু হিজরা শাকিব হিজরাই রয়ে গেল।,1,entertainment
দাড়ি ওয়ালা খানকিরপুতে ছেরাগো অপমান করতাছে পছন্দ হইলে লইবি না লইলে নাই। দাড়ি ওয়ালা খানকির পুতেরেই তো ছাউল্লা বাউল্লা কুত্তার মত দেখা যায় ও কি নিজেরে আয়নায় দেখছে,1,entertainment
সানাই দুধ অনেক বড় তাই একটা মাগি,1,entertainment
সাউয়া🖕,1,entertainment
"চুপকর শালি,মিষ্টি কুমড়া আমি খাই না।",1,entertainment
শালা তোর তো এটা নিয়ে ভিডিও বানানোর কোনো মানেই ছিল না৷ তুই একটা নষ্ট৷ কে কি করল তোর শরীর এত চুলকাই কেন৷ আমার কাছে মলম আছে আমি তোরে মোলম লাগাইয়া দিমু৷ আরে ঐ মেয়েটা একটা নষ্ট মেয়ে৷ তুই ইইউ টুব খুলছ একটা ভাল কিছু ভিডিও বানানোর চিন্তা করবে৷ আর তা না করে এই সব ভিডিও বানাস৷ ছি ছি ছি ছি ছি ছি৷ 👎👎👎👎👎👎👎👎👎👎😡😡😡😡😡😡😡😡😡😡,1,entertainment
জামাত আর পাকি জারজ এর বাচ্চারা ডিসলাইক মারছে।,1,entertainment
আবাল বিচারকের ভুল উচ্চারণ গুলো তুলে ধরার জন্য ধন্যবাদ ভাই।,1,entertainment
মাদার চোদ খুব ভাব চোদাই জাজ গিরি সোগার বিতর বইরা দিতে হয়,1,entertainment
বিচারোক গুলি মাদারচোদ,1,entertainment
বুঝলাম না কোন খানকির পোলা এদের কে জার্জ মেড করছে এই জার্জ গুলো মেবি নিজে দের চেহারা কখন ও আয়নায় দেখে না আবাল চুদা যতসব,1,entertainment
পরী মনি বাল কাটে না আবাল মার্ক,1,entertainment
খানকিক পোলা মাইয়া গ কে বানাই ছে জাজ,1,entertainment
তিশা মাগি কি ওরনা পরা বাদ দিয়া দিছে,1,entertainment
এগুলা আর কতো দেখমু পাগল ছাগল ইউটিওবার,1,entertainment
মাদার চোদ গুলারে কুতা দিয়ে চোদাব।,1,entertainment
প্রভার ওই ভিডিওটা আমিও দেখেছি ।একটা খানকি মেয়ে টাকার জন্য সব কিছুই করতে পারে।,1,entertainment
এই শালাকে জুতা দিয়ে পিটান সবাই,1,entertainment
শালারা একদম ফালতু । বিচারকদের কোন যোগ্যতাই নাই।,1,entertainment
আমি ঔ খানে থাকলে সব শালার মুখ জুতা খুলে মারতাম।।,1,entertainment
নাটকটা য়ে লিখেছে সে শুরের বাচছা,1,entertainment
এই হল বিশ্য মাগি,1,entertainment
"হোগার নাতিরা বালের নাটক বানাইছে, সময় টাই নষ্ট করলাম",1,entertainment
আমার বালের মুভি। তামিল মুভি নকল কইরা কাহিনী চোদাস খাংকির পোলা,1,entertainment
খানকির পোলা তোর ব্যবহারে এরকম কেন বে ও খানে তো ভদ্র গুলা গেছে সব আমি গেলে তরে লাত্থি মারতে খান্কি মাগির পোলা চেটের বিচারক তুই,1,entertainment
জাজ হইছে যার দাড়ি আর চুলের ঠিক নাই।।।।মাদার চোদ একটা,1,entertainment
এডমি আপনি পাবলিককে কি বুঝাতেছেন রাজিব অপুর্ব চোদে প্রভার বোদা পাকা করে পেলেছে এখন প্রভার বোদায় হাতির ধন ডুকালেও সমস্যা নাই হয়তো আবার কারো সাথে চোদা দিয়ে গোসল করেছে?,1,entertainment
সব কয়জন আমার শালা শালি,1,entertainment
কামলাচুদা ইউটুবার। তোরেতো মিথিলা ভিডিও কল দিয়া কইছিল।,1,entertainment
পাগলদের সাথে থাকতে থাকতে সালার ডাঃ গুলি পাগল হয়ে গেছে,1,entertainment
আরে কানকির পুলারে আর কানকি মাগিরে পাচা দিয়া করা দরকার,1,entertainment
অই হালার পুত নাকি ভিলেন নাকি ছেটের বাল গান্ডু,1,entertainment
"পাগলা ছুদা নায়ক,,,নায়কের কোন ছুদাই না,,, মাহিকেএকদম বাজে করে দিচ্ছে ফালতু নায়কদের সাথে অভিনয় করিয়ে,,",1,entertainment
আবাল চুদদা বিচারক আসলে সত্যি বাংলাদেশের ডাইরেক্ট আবাল চুদদা আপনারা ও কি আবাল হেয়ে গেছে,1,entertainment
আরে পাগল তুই হিরো আলমের নাম বললি কেন হিরো আলম তো একটা পাগল।,1,entertainment
বিচারক মাদারচোদ গুলাকে ছেরা জুতাদিয়া পিটানো উচিত,1,entertainment
পপির দুধ গুলো খুব বড় বড়,1,entertainment
মাদারচোদ সাকিব,1,entertainment
কেনো আপু ভাবি আন্টি<br /> খালা মামিবোন সেক্স করলে আসো <br />ভোদা চুষে লাল করে দেবো আমার ইমু নাম্বার +966537539937,1,entertainment
সবনম ফারিয়া হইছে একটা অস্ট্রেলিয়ান গাভী আর মম একটা দেশী মাগি আর দারি ওয়ালা টা হইলো একটা গাঞ্জা খোর খানকির পোলা 🐒,1,entertainment
বালের তুরে সামনে পাইলে মাথার উপর মুইতা দিমু বালের গান,1,entertainment
এই মাগী এই সব কি করে ছিছি,1,entertainment
এদেশে ত খাংকির লাইসেন্স দেয়,1,entertainment
মাগির বাচছা মাইরা লা,1,entertainment
তাইরে পাছা দিয়া করলে ঠিক হইহা যাইবো,1,entertainment
হট ভিডিও সেক্স করতে চাইলে আমার আইডি তে কন দাও ঃ,1,entertainment
তুই নিজেও তো কুত্তালীগ করিস,1,entertainment
আরে খানিক মাগি তর কি জগ্যোতা তুই আবার মাদার তেরেশা কথা বলসিস খানকি মাগি তর দুদ কে টেনে ছিরে দিব,1,entertainment
খানকির পোলা গাঁজাখোর,1,entertainment
তোর হ্যাডাটা ফাটাবো 😂😂😂,1,entertainment
খানকি মাগি মিথিলা,1,entertainment
বালের ছবি করে হালার পুতেরা অপরাধি মরে না,1,entertainment
পতিতা মাগি,1,entertainment
অৱে অৱ বাপে চোদে তাৱ কাৱনে অৱ দুধ বড়,1,entertainment
এই মাগী জালয় জুবো সমাজ নষ্ট হয়ে জাচ্ছে। খালি নুনু খারায়,1,entertainment
ভোদা তুই বোদা বেসস,1,entertainment
কি বালের গান এটা ইসস,1,entertainment
বিচারক সবগুলো ফকিন্নির বাচ্চা ফাজিলের বাচ্চা,1,entertainment
ভালো একটা খানকি সালা বাল এর ভাইরাল চুদার সময় নাই। আই সব খানকিগো।,1,entertainment
ওই ভাবিকে চুদে দিলে ভালই হত,1,entertainment
"শালা বাইঞ্চুদ, বালের ছবি, কুত্তার বাচ্চা",1,entertainment
এই শালিরে রেল মন্তির কাছে নিয়া জান,1,entertainment
খানকির পোলা জোরে দে,1,entertainment
বালের শো মদন রা নাকি বিচারক,1,entertainment
সানাইকে যদি মজা মতো সোনা দিয়ে চুদতে পারতাম।।।এই মাইয়ার দু গোব,1,entertainment
সানিতা এক টা মাগী,1,entertainment
বানচোদ তুই অন্যর চউল নিয়া কথা কস তুর চুলের অবস্তা কী কাওয়ার বাসা বুকাচুদা,1,entertainment
শুধু প্রবাসীদের অপমান খানকির পোলা,1,entertainment
সায়লা যদি এমপি হত পতিতা আনাগুনা ভেরে যেত,1,entertainment
ফাহমি হচ্ছে রিয়াল খানকির বাচ্ছা ওর ভাগ্য ভালো আমি একানে যাইনাই নইলে সালাকে আমি ওনাকেই তাপরাইতাম 😆,1,entertainment
পতিতা সানায় কে তার মোবি মোকতি দেয়া হবেনা নিসেদ করাহক জেই পরিছালক বানাবে তার কোনু মোবি মকত্তি দেয়া হবেনা,1,entertainment
সানাই তোরে চুদবো,1,entertainment
মিথিলা এখনাে ভার্জিন তাহলে তাে মিথিলার বােদার ভিতর কচু দােকানাে দরকার তাহলে মিথিলার চুলকানি জাবে।,1,entertainment
আমার তো মন চায় হেতির দুই দুদের পাহাড়ের উপর উঠে জাপটা দিয়ে পরে মরি।,1,entertainment
ওর তো দুধ ছাড়া আর কিছু নেই খানকি একটা,1,entertainment
ভিতরে কি বার্মিজ কম্বল ঢোকাইচে নাকি শালী।,1,entertainment
তুইতো সাবনুর ত দুরের কথা তুইতো ময়ুরীর যোগ্যনা তুই পতিতালয়ে যা,1,entertainment
দাঁড়িওয়ালা বস্তির ছেলে টা কে শবনম ফারিয়া মাগীর সাথের গাঞ্জট্টা টারে তো জীবনে কোনদিন দেখি নাই।,1,entertainment
মাগি তুই আবার দেশের জন্য কি বাল ফালাইছিস দুধু ফুলিয়ে দেখাইলেই কি দেশপ্রেম হয়,1,entertainment
আরে মাদারচোদ এই গুলোতো যুবো সমাজ ন্ষ্ট হইচ্ছে,1,entertainment
আমাদের নাম হলো বাঙালি আমাদের পাছা বাদামী 😂😂😂😂😂😂,1,entertainment
ভাই সোনা রানা।,1,entertainment
মিথিলা একটা খানকি মাগি এটা সাবাই জানে পতিতালয়ে তার স্থানও হবে না ছি ছি,1,entertainment
"আবালদের কমেন্ট পড়ে না হেসে পারলাম!আবাল আবুলের বাচছারাধর্ম নিয়ে তোদের এত চুলখানি!তা হলে ফেসবুক নাটক সিনেমা দেখছ কেন!সব কিচুতে ধর্মের চুলখানি,আবুলের বাচছা আবাল রা।",1,entertainment
এই সানাই মাগি তর ফুন কিলা মুটা নি,1,entertainment
কুত্তার বচ্চারা আমার সুনার ছবি বানাইছে বাইন চুদেরা। মাদার চুদ,1,entertainment
বিচারের জন্য সব কুত্তা নিয়া আসছে নাকি,1,entertainment
জয় ভাই এই খানকি বাংলাদেশ এর ভালো চায়না ও বিধর্মী দালাল ওকে বাংলা থেকে জুতা পিঠা দিয়ে তাড়াইয়া দেয়া হোক।,1,entertainment
এই মেয়ে তো খারাপ মানি একটা খানকি,1,entertainment
শালিকে জুতা খুলে মারার দরকার ভাই,1,entertainment
ভাই আপনি অসাধারণ ভিডিও বানিয়েছেন আপনাকে ধন্যবাদ যেমন কুকুর তেমন মুগুর।,1,entertainment
বিচারক একটা ছিল তিন বিচি ওয়ালা মেয়ে দুই টা ছিল হালা গো রে জুতা মারার দরকার ছিল,1,entertainment
চ্যালেনআই মত এত সুন্দর একটা জনপ্রিয় টিভি শোতে এরকম চারটা গাধাদের সিলেক্ট করবে এটা আমরা আশা করিনি,1,entertainment
মিথিলা কে বাংলাদেশে ডুকতে দেওয়া হবে না কারণ সে খোটা মুসলিম জাতির কলংক হিংদু কে বিয়ে করচে সে একটা মাগি মাগি মাগি মাগি মাগি মাগি মাগি মাগি মাগি মাগি মাগি মাগি মাগি,1,entertainment
ওর বাবা একটা মাগির দালাল ছিল,1,entertainment
দাঁড়িওয়ালা ছাগলটা ফার্স্ট ক্লাস বেয়াদব আর মমো সবনম এরা তো মামুলি অভিনেত্রী যাদের বিচারকের চেয়ারে বসার কোন যোগ্যতাই নেই । কথাই আছে না ফকিন্নি হটাৎ করে বড়লোক হয়ে গেলে সে আকাশে উড়ে ।,1,entertainment
হুম মিথিলার মেয়ে টা সৃজিত এর পাছা দিয়ে বের হয়েছে তো তাই,1,entertainment
দুইটাই জারজ,1,entertainment
আমাদের দেশে অনেক ইসলামিক নেতা লোকেরা আছে বিভিন্ন বিষয় নিয়ে ইসলামের পক্ষে হাউ কাউ করে চিল্লায় যদি তাই হয় তাহলে এসব খানকিদের কে ইসলামের নেতারা কিছু বলে না কেন,1,entertainment
সালি তর মতো মিয়েদের থাইল্যান্ড পাঠানো ইচিত,1,entertainment
শালা উচ্চারণ টিক করতে বলছ নিজের টা টিক করে আয় গো হুম মানে কি শালা মুর্খ,1,entertainment
দাড়িয়ালা এই মাদারচোদ বিচারকটা কে হালা কোথা থেকে আইছে 😡,1,entertainment
কি আমার সোনার নায়িকা বাংলা ই বলতে পারে না ঠিকমত আবার কথায় কথায় ইংলিশ চোদায়,1,entertainment
নদীর নাভীর হুলাক টা সেরকম,1,entertainment
তোদের কি আর কাজ নাই বাল এর চ্যানেল গুলা অন্য কিছু পাস না এইসব তো বেশ্যা মেয়ে নিশে মাতামাতি না করে চকবাজার আগুনে পূরা অসহায় মানুষের পাশে যা তাদের ফেমেলি নিয়ে কিছু কর যেন ভাল তারা এই সব বেশ্যা নিয়ে গাঢাগাঢি না করে,1,entertainment
মোমো আর দাড়িওয়ালা ছেলেটার আচরণ দেখি কুত্তার মত। এগুলারে বিচারক করছে কে,1,entertainment
বালের ভংগী ধরস শালা তুর কথা ঠিক কর।,1,entertainment
যারা আনলাইক মারছে মুভিতে তারা জারজ,1,entertainment
এই কুত্তার বাচ্চা হলো বাবা খোর দেখেন না চোখ ডলে মাথা ডলে কুত্তার বাচ্চা সত্যি সত্যি বাবা খোর,1,entertainment
শবনম ফারিয়া একটা খানকিমাগী,1,entertainment
ওরে চুদে মজা পাওয়া যাবে,1,entertainment
ধন চুষা বেডি গুলা নিয়া আইসে,1,entertainment
বুবলি একটা খানকি ওর মতো নায়িকা চাইনা,1,entertainment
যদি অভিনয় করতে আমি যেতাম তাহলে আর এই রকম বাবে ব্যাবহার টা আমার সাথে হতো রে তাহলে দেকলি বাইনচুদ গাঁজাকুরের দল তরা সব কয়টারে জুতা পিটা করতাম,1,entertainment
"প্রিয় নায়িকা,কিন্তু নায়ক হেডা একটা আবাল।বালের অভিনয় করে",1,entertainment
তানিয়ার দুধ গুলি 🙈🙈🙈🙈🙈,1,entertainment
খানকির মুখে জাতির কথা মানায় না,1,entertainment
তোমাকে হাতির দোন দিয়ে চুদবো মাগী,1,entertainment
বলদ মার্কা পরিচালক।,1,entertainment
ওর সোনা দিয়ে কলা দিব আমি মাগি জাহান্নমেরে বয়নাই তোর মাগি তোই মরবেনা শালি,1,entertainment
বিচারক খানকির পোলা গো জুতা দিয়া পিটানো উচিৎ,1,entertainment
সাসালার পোরা কই ভিডিও,1,entertainment
তরে ত কুকুর ও চুদবো না খানকি,1,entertainment
আল্লাহই ভালো জানে এসব পতিতার জন্ম কেনো দিয়েছে 🤔,1,entertainment
"পাছা মোটা, স্তন মোটা মেয়ে আমার একদম পছন্দ নয়।আর সেটা যদি হয় শবনম ফারিয়া তাহলে কোন কথাই নেই",1,entertainment
তাহসান একটা বাল,1,entertainment
সালার দাদা আমার সাথে গেইম খেললো 😂😂😂😂,1,entertainment
বিচারক কি বাংলাদেশে অভাব রয়েছে কি সব ফালতু নোংরা টাইপের প্রতিবন্ধীদের বিচারক বানিয়েছে 😂😂🤣🤣 একজন মানুষের সাথে কি ভাবে আচরণ করতে হয় সেটি বিচারক নামের প্রতিবন্ধীরা মনে হয় ভুলে গিয়েছে একজন মানুষ কে বিনা দোষে অপমান করা কোনো মানুষের অধিকার নেই,1,entertainment
এই হালায় ব্যশ্যার পুত,1,entertainment
বাংলাদেশের পরিচালক গুলো নটির ছেলে।আর নায়িকা গুলো আরো নটি মাগি,1,entertainment
তোমার নানির সোনা,1,entertainment
বিশ্ব পতিতা কে বিয়ে করলো রাঙা মস্তান জাপা নেটা,1,entertainment
এগুলা খানকি,1,entertainment
কানকি মাগি আর ছুদির বাই সাউয়ার জাযগিরি করতেছ,1,entertainment
মমোর মায়েরে বাপ ফাহমির মায়েরে বাপ এই বিচার কার্যে যে শালার পুত ছিলো তার মায়েরে বাপ,1,entertainment
আমি হলে জুতা ছুরে মারতাম ওদের পিছুনে মাসুদ রানা দেখা বয়েই গেছে হারামজাদা ব্যবহারে এত নোংরা,1,entertainment
বাজ‌ে মম ফার‌িয়া অার পাগলা ভ‌েড়া অায়না দ‌িয়ে ত‌োগ‌োচে‌হারা দেখ,1,entertainment
এই নি সেই বালের জায়েদ খানের ছবি। lol,1,entertainment
পাগল ছাগল বিচারক মন্ডলি,1,entertainment
সালার আমরা টাকা দিয়া ভারা করে টিপাইতে পারিনা আর অনি লাখ টাকা দিয়া ধুত ভর করছে কেনো বাংলা দেশের সোপ পোলারা কি ভদ্রলোক হইয়া গেছেনাকি,1,entertainment
ওরে জুতা মারা দরকার সালা বিচারক,1,entertainment
এসব ছাগল বিচারকের জন্য দেশে শিল্পী তৈরি হয় না।,1,entertainment
এদের মত।নডিদেরকে সুদু চেকস বিডিওই মানায় আর কিচুি না আর কোন কুততারা যে এি সুব নডিদের ইনটার বিও নেয় যানিনা,1,entertainment
তোর বিচারকরে চুদি,1,entertainment
সৃজিত কুত্তার বাচ্চা,1,entertainment
সানাইকে সবাই বলে অনেক সুন্দর আসলে কি ও এত সুন্দর ওকে দেখলে আমার অনেক রাগ ওঠে ওর বডি দেখছেন কত খারাপ ওর পাছা দেখছেন কত খারাপ চুদানি ওদের মতন গোয়া টা বড় মানুষ কি দেখে পাগল হয় ফালতু মেয়ে সে কি বুঝে না আজকাল বছরের কিশোর কিশোরীরা মোবাইল ইউজ করে ঠিক টাইমে বিয়ে হলে ওর বাচ্চা ও মোবাইল চালাতে পারতো প্লিজ সরি খারাপ নজরে দেখবেন না,1,entertainment
সালাদের বিচারক কে বানাইছে। হালারা নুচড়া নুচড়ার দল।,1,entertainment
এরে সানাই তোরে বলছি ছেকছ বিডিও করতি আমি দেকতাম একটু,1,entertainment
সানিতা মালে দানা পরেছে তাই এই অবস্থা,1,entertainment
খানকির বাচ্চার জন্মগত প্রবলেম আছে মনে হয়,1,entertainment
সালার বিচারকদের সবাইকের এক চামচ গু খাওয়ানো উচিত সালার পুতেরা,1,entertainment
তুই রাস্তার মাগী,1,entertainment
একলা একলা তোরমার বোদাদেখবো সালা মাদারচুদ,1,entertainment
যত সব হাগল ছাগল।,1,entertainment
"সেটাই।খুব জঘন্য নোংরা মিথিলা। আমিও একটা মেয়ে ‌। ভাবতেই খারাপ লাগে কিভাবে একটা মেয়ে এত পুরুষের সংস্পর্শে যেতে পারে। ছি!!! জীবনে কত চড়াই উতরাই পার করলাম, তবুও একজন স্বামীর ঘর থেকেই কবরে যাব ইনশাল্লাহ।",1,entertainment
এরকম বলদ নায়িকা বাংলাদেশে কেমনে থকে ওর মানুষিক রোগের ডাক্তার দেখানো দরকার,1,entertainment
ওরে ঘোড়া দিয়ে চোদাতে হবে,1,entertainment
হাইরে হালার পরিচালক হালা নিজেও গানজা খোর আর নায়ক ও আনচে একটা গানজা খোর।<br />আমিন খান মেন নায়ক হলে ছবিটা আরো হিট হতো।,1,entertainment
চুদা খাওয়া নাইকা,1,entertainment
আবালের বাচ্চাগুলোকে জুতার বারি দিয়ে ব্যবহার শিখানো উচিৎ।,1,entertainment
খানকি মাগীর বাচ্ছা ইসলাম কি বোঝস খানকির বাচ্ছা খানকি,1,entertainment
সব চুতমারানি বিচারক,1,entertainment
পরিচালক মাদারচুদ,1,entertainment
খানকিরে ভাদ্রমাসের কুত্তা দিয়া চুদানো লাগবো।তাহলে মাগির ভুদার খাইজ কমবো।। সানাই আহো তুমারে দিয়া পয়সা কামাই।,1,entertainment
মাগির বাচছা মাগি,1,entertainment
দুইটাই দুধওয়ালা অস্ট্রেলিয়ান গাভীর মত লাগে দুইটা কে,1,entertainment
মাদারী পরিচালক,1,entertainment
সানাই আপু তোমার অইটা একটু হাতাইতে দিবা,1,entertainment
মাগির বাচ্চাগুলোকে বিচারক হিসেবে কে আনছে 😠😠😠,1,entertainment
বুবলির ভোদায় এসিড নিক্ষেপ করা উচিত।,1,entertainment
আরে জানোয়ারের বাচ্চারা তোদের কি যোগ্যতা আছে রে তোদের একটা গান গাইতে বললে তো ছাগলের মত ব্যা ব্যা করবি।বাইনচোদের বাচ্চারা।বাল ফালাইতে আইছে এখানে।,1,entertainment
বাল,1,entertainment
এখানে কে কে বুকাচুদি ফারিয়ার ফ‍্যান আছিস কমেন্টে আমাকে গালাগালি দিয়ে জানা,1,entertainment
সানিতা তুমি ত পোলাপাইনের চোদা খাইতে খাইতে তোমার ভুদার অনের বড় কইরা ফেলাইছ তোমার দুধ ত অনেক বড় বড় হয়ে গেছে আমি তোমাকে চোদব কত টাকা লাগবে বলচোদে চোদে তোমার ভুদা রক্ত বের করব ওফ ওফ ওফ কি মজা,1,entertainment
বৌ এর দুধ এর চাপায় জামাই নিহত ।😅😄😃😂😁,1,entertainment
বলদ চোদা জাজেস গুলোরে ধরে জুতা খুলে মারা উচিত। মিডিয়া মাদারচোদ খানকির পোলা গো এই বাল ছাল সো প্রোডিউস না করে এর চেয়ে চোদা চুদির ভিডিও প্রোডিউস কর খানকির বাচ্চারা। আবার স্টেজে বড় বড় ভাষন চোদাস বাংলা চ্যানেল বাংলাদেশী রা দেখে না কি দেখবে তোদের বাল চোদা সো দেখার টাইম নাই এই সো তে জাজ গিরি সো প্রোডিউস না করে এর চেয়ে হোটেলে গিয়ে মেরে আই তারপর ও আমাদের জালাস না।,1,entertainment
ভাই মিথিলা কে এই বাজে মেয়েটা কে আমরা কেন এত ভাইরাল করছি,1,entertainment
নিচ তালা ভাড়া দিয়ে উপরে তালা বড় বানাইছি। মাগি বলে কি,1,entertainment
এই খানকির পুলারে কোন মাদারচোদে বিচারক বানাইছে একটা পতুতা আর মাগির দালালদের দিয়ে বিচারক আর উপস্থাপন করা হয় খানকি মাঘিরা খানকি মাঘির পুলারা। তোদের বাবায় তোদের মাকে চুদার সময় এদিক ওদিক করছিলো তাই মানুষের সাথে ভালো আচরণ কিভাবে করতে হয় তা ভুলেই গিয়েছিস কুত্তার বাচ্ছারা।,1,entertainment
"ধুর মাদারচোদ , বালের মুভি বানাইছস, শাওয়া",1,entertainment
ছাগলা মডেল।,1,entertainment
শালিকে পুগা মেরে দে,1,entertainment
জুতা মারা উচিৎ শুয়ার বাচ্চা দুইটাকে এই বিষয়টা নিয়েও মানুষের ইন্টারভিউ নেয়া লাগে।আল্লাহ এমন মেয়ে মানুষকে তুমি তুলে নাও।এ কোন দুনিয়ায় বাস করছি আমরা যে মেয়ে হয়ে মেয়ের সম্মান নষ্ট করছে। অসভ্য সমাজ অসভ্য রুচি।ছি বেহায়া।,1,entertainment
তোগো বিচারকের মারে চুদি মাগির পোলারা সাউয়ার মাসুদ রানা।,1,entertainment
আচ্ছা ফারিয়ার সাথে এই ছাগলটা কে জীবনে ও তো এই আবালকে দেখি নি।,1,entertainment
"মিথিলাকে কোন মানব অথবা কোন রক্ত মাঙশের সৃষ্ট পশু দ্বারা চুদিয়ে তার কাম রস নির্গত করা ইহা কখনো সম্ভব নহে একমাত্র কিছু দানবীয় জীন ভূত পিশাচ,,, দেও দানব,,অপদেবতা এবং ইবলিশ শয়তানকে দিয়ে চুদিয়ে চুদিয়ে তার কামরস নির্গত করাই সম্ভব ।।",1,entertainment
ভাই আমার মতে মিথিলাকে ঘোড়ার সোনা দেখাতে হবে,1,entertainment
ও একটা বাইনচোদ । শরির দেখিয়ে জনপ্রিয়তা পাওয়া যায়না । জনপ্রিয়তা পেতে যোগ্যতা প্রয়োজন । ওর কোন যোগ্যতাই নাই তাই এসব অস্লীল কিছু করে আলোচনায় থাকতে চাচ্ছে ছিঃ ছিঃ,1,entertainment
এক পায়ে নূপুর ছবিটির পরিচালক আস্তা একটা আবাল চুদা বিয়াক্কেল কোন কাহিনী ছারা আচুদা একটা মুভি বানাইছে।,1,entertainment
এত বড দুধ দিয়া কি করবি মাগি,1,entertainment
রেন্ডি জারজ সন্তান,1,entertainment
আবাল মার্কা নায়ককে দিসে হিরো খাজাখোর পরিচালক,1,entertainment
যারা খারাপ কমেন্টস করতেছে তাদের বলছি তোরা যে আসলে আবাল 😏কেননা ইসলামে শুধু অশ্লীল পোশাকে গান বাজনা করাটাই পাপ না সকল প্রকার গানবাজনা হারাম তোরা কোনো ধরনের গান শুনবিও না দেখবিও না শুধুমাত্র রেডিওতে দেশের খবর শুনবি তাহলেই তো হয়।😉,1,entertainment
পরীচালক কি পাগল না ছাগল মানুষ টাকা দিয়া এসব ছবি চাযনা ছবি চায় ময়ূরীর মুনমুন নের ছবি চায়,1,entertainment
রংপুইরা মাগিত এইজন্যই সস্তা টাকা দিলে পাওয়া জায় তাইতো,1,entertainment
হিরন একটা মাদারচুদ,1,entertainment
আমার হাতে একটা বেত থাকলে ওদের সবার পাছায় ক্রস ক্রস করে কয়েকটা মারতাম! যেমনে ওরা পোলা পাইনের পাছা চেক করে!,1,entertainment
বিচারক যদি এত মাদারচোদ হয়। মাসুদ রানা কে তো খুজেও পাওয়া যাবে না,1,entertainment
এসব আবালচোদা বিচারকদের কুত্তা পিঠা দেওয়ান দরকার,1,entertainment
এখানে মেয়ে বিচারক মাগি পতিতা গুলাকে আমার কাচে পাঠাও আমি চো,1,entertainment
নিউ জেনারেশন দারা হবে শুধু টাইট ব্রা,1,entertainment
সব বিচারকগুলো এক একটা ছাগল।,1,entertainment
এই জাজ্ গুলো তো এক একটা বাংলা জানোয়ার,1,entertainment
আমারী একী কতা আমিন খানের মত সুপার হিরো তাখতে এই ছবিতে আরেক ছাগলের মত নায়কের কী দরকার এই হালারে গাজা খোরের মত লাগে হেতে বুলে হিরো সালার কী বলব বাংলাদেশর পরিচালক দের যাকে মনে চায় হেতেরে নায়ক বানায় এই ছবি মনে করেছিলাম দেখব আমার পছন্দের নায়ক আমিন খান কিন্তু এখন দেকি এই পাগল ছগল নায়ক এরেক টা দেখতে মন হয় চিকন আলির মত।,1,entertainment
এতো সব গাধা গরু ভেড়া মহিষ ছাগল পাগল মিডিয়ায় আসে কেমন করে আবার হয়েছে বিচারক এদেকে ধরে বিদেশি নয় দেশী কুত্তা দিয়ে মারানো দরকার😫😫😫😫সাধারন ছেলে গুলো কতো আশা নিয়ে গেছে ওখানে মাসুদ রানা হতে না পারুক কিন্তু এভাবে অপমান করার কারন টা কি,1,entertainment
খানকির আবার কাজ নিচতালা ভাড়াদিয়ে যা করে তাই হেতি করে,1,entertainment
বাংলাদেশের এক নাম্বার মাগি সে,1,entertainment
বেটার জীবনে প্রথম এইজন্য এজন্য ভার্জিন মনে হয়েছে যার একটা বাচ্চা হয়ে যায় সে কিভাবে ভার্জিন থাকে ভার্জিন কারে কয় ব্যাটা চেনে না ওটাতো বোকাচোদা,1,entertainment
ফালতু একটা মেয়ে,1,entertainment
বোকাচোদা বাঙালি।এরা ইলোমিনাতি। আর এরা ইবলিস এর পূজা করে। আর তোরা খানকির পোলারা ওদেরকেই প্রোমোট করছিস। মনে রাখিস আল্লাহরর ধরা বড় ধরা।,1,entertainment
ওতো গাঁজাখোর কুত্তার বাচ্চা ও নিজে গাজা খাই সেজন্য সবাইকে গাঁজাখোর মনে করেছিল,1,entertainment
এই শালারা কি বিচারক না খাটাশের দল ওটাকে ধরে পাছাই মারলে সবগুলো সোজা হয়ে যাবে,1,entertainment
এ মাদার চোদ ছেকচের ভিড়িও 23 মিণিট ফালটো গেলো,1,entertainment
তোর চেলেন তুই দেখ সালার বাচ্ছা রা মানুষ কে অপমান করতে তোদের গ্রিনা লাগে না কয়কটা জানোয়ার কে দিয়ে মাসুদ রানাকে খুজছিছ লাভ নাই জীবনেও একটা মাসুদ রানা পাবি না কুত্তা মিডিয়া,1,entertainment
রাজ ভাই থেকে শিখ বাকীরা যতসব আবালের দল।রাজ ভাই সেরা দাড়ি ওয়ালা চান্ডাল তোমার অনেক কিছু শিখার আছে,1,entertainment
কমেন্ট পড়তে আসা কেউ যদি নেক্সট এপিসোড এ অংশ নিতে যান তাহলে যাওয়ার সময় অন্তত কয়েকটা ছেঁড়া জুতা নিয়ে গিয়ে এদের মত ফইন্নি মার্কা আবালদের মুখে মেরে আসার অনুরুধ রইলো।,1,entertainment
"তানভীর তুই মায়ের কবর জিয়ারত করতে এসে মহিলার ছবি তুলছ,,,, তুই আবার এলাকার ছেলে আমার বাল,,তুর কেমারা তুর পুটকির ভিতর ঢুকিয়ে দিতাম",1,entertainment
ওরে নেন্টা করে চুদে দিলেও ওটা এর কাচে নরমাল হবে কারন ব্যাসসার ঘর থেকে ব্যাসসা ই জন্ম নেয়,1,entertainment
পরদার বিসয়ে বুজিস কিছু মাগি,1,entertainment
জুতা দিয়ে মারো মাগি কে,1,entertainment
পতিতা আর মাগির দালাল দের বিচারক কে বানাইছে,1,entertainment
মেয়েরা সুদা দিলে মাগি হয়ে যায়৷ আর যে মাগি দেখলে লোভ সামলাতে পারে না৷ তাকে কি নামে ডাকা যায়৷৷ মাগিকে নিয়া কমেন্ট করার আগে একভার চিন্তা করুন৷,1,entertainment
যেই কুত্তার বাচ্চারা মাইয়াগ দিকে খারাপ নজর দিয়া তাকাবি তগ এমন কইরা গেন্দারি হান্দায় দেওয়া দরকার।,1,entertainment
কুত্তা বাচ্চা জারজ না হলে এমন করতে পারতো না,1,entertainment
তুরে পাইলে মাগি একশো কুত্তা দিয়া চুদাইতাম,1,entertainment
সব মাদার চোদ। জুতা পিটা করা উচিত,1,entertainment
"সালমান শাহ আজ বেচে থাকলে বাংলাদেশে সিনেমা হলের সংখ্যা হত 3000 এর উপরে। আপামর জনগন সিনেমা হলে দাড়িয়ে দাড়িযে সালমান শাহ’র ছবি দেখত।ঘাড় বেকা, হিজড়া ভোদাই খান সাকিব এত জনপ্রিয় যে, বাংলাদেশের 1,500 সিনেমা হলের সংখ্যা কমতে কমতে 175 রে গিয়ে দাড়িয়েছে।5বছর পরে বাংলাদেশে কোন সিনেমা হল থাকবে না।সালমান শাহ’র মত নায়ক এ দেশে আবার উদয় হলে সিনেমা হল বাচবে।",1,entertainment
সানিতা তুই মাগি মাগি মাগি,1,entertainment
খানকি মাগির বাচ্চারা। তোগোরে ফুটা কইরা ফালামু। আমার বালারে জাজ। মাদারির বাচ্চারা। ভালো অভিনয় করা মানে এই না যে তোরা একদম জাজ হয়ে গেছস। আমার বাল,1,entertainment
এই বালের মাসুদ রানা কে রে👿 আর এই ভাবে অপমান করার মানে কি বুড়িয়া জাজ টা বেশি অপমান করছে।জাজরা নিজেরে কি মনে করে🖕🖕,1,entertainment
সানাই বলল মাদার তেরেসা নাকি বলছে যে প্রকাশ্য মানুষকে ভালবাসতে পারে না সে আল্লাহকে ভালবাসতে পারেনা। তাই বলে কি তোর মতন একটা মাগীকে ভালবাসতে হবে। আর মাদার তেরেসাকে যে বলছে সেটাই মানতে হবে।,1,entertainment
বাল বানাইছও,1,entertainment
বাংলাদেশের কতগুলো পাগল ছাগল বিচারকের আসনে বসাইছে ওদের বিচারকের আসনে না বসিয়ে নাপিতের কাজ দিলে ভাল করতো ওদের কে জুতা মারা উচিত ওদের ব্যবহার শুনলে ওদের মুখে কুকুরে প্রসাব করবে,1,entertainment
কোন আবাল গুলায় আনলাইক দিল?,1,entertainment
এই মাগিকে নিয়ে সেফু দার আর একবার লাইভে আসার দরকার😂,1,entertainment
বিচারকদের বলতাছি তদের সবাইকে চুদি,1,entertainment
হালার পো লাল পানজাবি টারে দেখলে মনডা চায় ওরে মুগুর দিয়া পিডাই।হালা হুদাই হা হা হা করে গুরুর মতো,1,entertainment
জুতা মারার দরকার সালাগো,1,entertainment
মাদার চুদ সালারা এখানে কে আনছে এদের এরা নাকি বিচারক বাল ফালাইতে আইছে তাদের জিজ্ঞেস করলে কি অভিনয় করে দেখাতে পারত শালারা।,1,entertainment
আপু মানে দুধ সেটা বাংলায় বলেন । বাংলা ভাষার জন্য আমরা যুদ্ব করছি। তাই না বলে দুধ বললে ভালো হয়😜😜,1,entertainment
এ শালা রা এন্ড শালিরা বাংলাদেশ মিডিয়া টা শেষ,1,entertainment
প্রভারে যদি চুদতে পারতাম,1,entertainment
সালা জাহিদ তে বিলে নায়েক সালা ১টা ছাগল চোর,1,entertainment
"দশ বছরের আগের নাটক সালার পোত এইটা,,,,",1,entertainment
শালা তুই না বিচারক তুর মধ্যে কি আছে মাসুদ রানার হুদাই বাল ছিড়তে লই আইছে তোগরে হেমারচোদা।,1,entertainment
এই বোকা চোদাদেরকে বিচারোক হিসাবে কে 🤔🙄😜😋,1,entertainment
লুচ্চা সালা,1,entertainment
বুবলীকেমামামাগী,1,entertainment
নিচ তালা ডেলি কয় জনের কাছে বাড়া দেয় এটা জিগাছ করেনো কেনো।,1,entertainment
এই ধরনের বিচারক নামের খানকীর বাচ্চাদের সহ ওদের মা বোন বৌ কে কুত্তা দিয়ে চুদানো দরকার।,1,entertainment
নায়িকা ময়ুরীর নাভির মধ্যে একটা মানুষ ঢুকে যেতে পারে।,1,entertainment
পোলাপানগুলায় কেনো পিটাইলোনা খানকির পুলাদের,1,entertainment
যে চুদির ভাইয়েরা এবং বোনেরা তাদের জন্য আমার হাজারো তালি রাস্তা এটা তালি ছিল না,1,entertainment
এই চারজন এর মধ্যে একটা হচ্ছে হনুমান সালায় কয় বছর চুল দাড়ি কাটে না কে জানে। এই সালায় একটা ভন্ড মাজার পুজারি ওর বাপ মায়ের পরিচয় ঠিক আছে কিনা সন্ধেহ আছে,1,entertainment
চুদাচুদির ছবি টা দেখালেন না তো ?,1,entertainment
মিথিলার মেয়ে টা সৃজিত এর পিছন দিয়া হইছেই এজন্য মিথিলা এখন ভারজিন,1,entertainment
সালারপুত আগে নিজের মুখের ভাষা ঠিক কর তারপর ভিডিও বানাইস,1,entertainment
কানকির বাচ্চারা,1,entertainment
শালা কুত্তার বাচ্চা তুই কি মানুষ,1,entertainment
বোকাচুদা রা,1,entertainment
বালের রানা হাওয়ার জন্য এত অপমান ভাই চাকরি করলে কি হয়ে তোমাদের ঐ গুলা ত বিচারক না।,1,entertainment
ভাইয়া এই দাঁড়ি অাওয়ালা কুত্তার বাচ্চা নাম কি,1,entertainment
মাগির পোলারা এর ভিডিওগুলার কমেন্টগুলো একটু পইড়া দেখিস তোর মায়েরে কিভাবে পাবলিকের চোদে,1,entertainment
.কি ফালতু নাইকা কোন পার্সনালিটি নাই যার তার সাথে অভিনয় করে ওকে টাকা দিলেই সব হবে টাকা দিলে ওকে যে কেও ভোগ করতে পারবে খানকি,1,entertainment
ঠিক এটাই চাচ্ছিলাম ভাই মনে অনেক ক্ষোভ ছিল এই শাওয়ার জাজদের দের জন্য আপনি তালি বাজায়ে দিছেন আহা!! এখন শান্তি ❤ পাবনা 😎✌,1,entertainment
তোদের যদি পুটকি মারতে পারতাম জীবনে একটাই আশা,1,entertainment
ছাগল মাকা পরিচালোক এফডিসি আর কমিটুলা গাফক্লাব এ মভি শেস শালা ফকির মভির লাস্টে বাবার পতিশদ,1,entertainment
মাগিটা কি সুন্দর নীতি কথা বলে সে নাকি দেশের জন্য কাজ করের,1,entertainment
সানিতা আছিলো কি এখন হয়েছে কি সুজন সখির নায়কা সেই নাকাকে ১০ চুদলে কিছুহবে না আমি শরীয়াতপুরের ছেলে নড়িয়া বাড়ি,1,entertainment
তুই য়ে তোর মা বাবা গালে জুতা মারচোত মাগি রে বাঁশ বরে দে,1,entertainment
বাজারর মাগি,1,entertainment
কি বাল নাচ ছো মাগি হাহাহাহাহা,1,entertainment
তানজিন তিশা একটা শালি একজনের ঘর ভাঙতে চায় শালি কে নেংটা করে চোদো,1,entertainment
অসভ্য অযোগ্য বেয়াদব নেশাখোর পাগল জাজকে যারা গণপিটুনি দিতে পারবে তাদের মধ্যে একজনকে মাসুদ রানা দেওয়া হোক।,1,entertainment
যতসব ছাগলকে বিচারক বানাইছে,1,entertainment
শালি কি কাপড়ে আলাহ নাম লয়।,1,entertainment
কি বলবো বুঝতে পারছি না আমি গালি দিয়ে আমার মুখ খারাপ করতে চাইনা জাজে রা সব আবার চোদা,1,entertainment
এমবি না হয়ে চুদা নে কাংকি মাগি বে্র্ষা,1,entertainment
সব গুলো বাইনচুদ কুত্তার বাচ্চা,1,entertainment
বাংলার কারিনা কাপুরচুপুর😜,1,entertainment
জুতা মাইরা কপালের চারা ফাটাইয়া ফালানোর দরকার আবাল চুদা বিচারক,1,entertainment
বিচারক গুলা মনেহয় কুত্তার চুদা😠😠😠😠😠😠😠😠😠😠😠😠😠😠😠😠😠😠😠😠😠😠😠😠😠😠😠😠😠😠😠😠😠😠😠😠😠😠😠😠😠,1,entertainment
জেই সুয়ুরের বাচ্চা গুলা বিচারক ওই কুত্তার বাচ্চা গুলা তো কথায় বলতে জানে না ভালো মায়ের গরে কুত্তা জন্ম দিছে,1,entertainment
এ সব শুয়োরের বাচ্ছারা যে নিজেদের কি মনে করে তা এরা নিজেরা ও জানেনা কেবল শুরু তাই এই অবস্থা থাক আর বেশী কিছু বলবোনা,1,entertainment
পরিচালকের মায়রে চুদি ড়িরকটারের মায়রে চুদি,1,entertainment
সবগুলো মাদারচোদ আর খানকি মাগি,1,entertainment
চুরের বড় গলা মাগী দু তালা ওয়ালা 😋,1,entertainment
বিচারক গুলাকে জুতা পেটা করা উচিত বিচারক চুদইছে পকিন্নির পুতরা😁😁😁,1,entertainment
সকাল বিকাল ঝাড়ু মারলে কিছু শিখবো এই সমস্ত কুলাংগার বালের বিচারকরা।আর মম শবনম তোমরা অভিনেত্রীই তো হতে পারলানা আবার বিচারক কবে হইলা শ্যাম অন ইউ।,1,entertainment
ফাক দেট জংলি মাদারফাকার!,1,entertainment
তরা মনে হয় গাজা বিজায়া খাইছস । দুনিয়াতে কতো ধরনের পাগল দেখমু ।,1,entertainment
মম বাংলার মাগি,1,entertainment
তোর জীবনে মেয়ে চুদলিরে সাকিব,1,entertainment
ফাহমির মতো একটা পাগল বাষ্টার্ড কিভাবে জাজ হয়।,1,entertainment
জোরে দে খানকির পোলা😎,1,entertainment
ছাগল কোথাকার,1,entertainment
"হেতেড়ে জুতা মাড়া দরকার,,",1,entertainment
মাদারসুদি জাজ এরা ভাই ফুল ভিডিও দেখে খুব কষ্ট লাগছে একটা গালিও দিলে না সব গালি ভুলে গেছো নাকি ভাই।,1,entertainment
বিএনপি নেত্রী হট সেক্সি শায়লা।,1,entertainment
এই খানকির বাচ্চাদের মাইরা ফেলাই একবারে কুত্তার বাচ্চাদের ইন্ডিয়া পাঠায় দাও,1,entertainment
খানকির পোলা ভুয়া ভিডিও তৈরি করার,1,entertainment
মাগি মত নাচ ভালো লাগেনা,1,entertainment
বানচোদ দল গোলো বিচারক বানাইসে কে গাজা কুর একেকটা শোতে গাজা খায়,1,entertainment
সালা রে দরে গোয়া মারার দরকার বিচারক,1,entertainment
দাড়িওয়ালা মাগীর পুলা নটির পুলারে পাইলে জুতা দিয়ে পিটাইতাম,1,entertainment
হালার চেহারা বানরের মত,1,entertainment
বালের ছবি করছে কোন ডাইলক করতে পারেনা কোন অভিনয় করতে পারে না বাজে ছবি,1,entertainment
পাগলে কিনা বলে ছাগলে কিনা খায় মান্নার কত ছবিতে ইলিয়াস কাঞ্চন ছাইট নায়ক আছে এই ছবিটাও মুল চরিএে মান্নার ভাল করে দেখ পুরা কাহিনিটাতো মান্নার,1,entertainment
আপনি কি আপনার দুধ বিক্রি করবেন প্রতি লিটার টাকা দিবোনে,1,entertainment
দুই মাগিই খারাপ খাসটা,1,entertainment
বেষ্ট ইমপ্লান করে এই খানকি দুই কেজি দুধ দশ কেজি বানিয়ে ভাইরাল হতে চাইছে। তয় খানকি দুধের ভিতর কাপগ গুইজ্যা নিয়া আইছে ফহিন্নি খানকি ইমপ্লান করতে কিভাবে পারে। এটা করতে টাকা লাগে।,1,entertainment
এই মেয়েতো মাগি,1,entertainment
সব গোলো জানোয়ারের বাচ্চা জানোয়ার পতিতা বদমাইশ ভাল করে খবর নিয়ে দেখেন পতিতা গিরি করে এই পর্যন্ত আইছে,1,entertainment
এদের কে দেশ থেকে হটাও হিজরা জাজ যত্তসব 🇧🇩ধন্যবাদ তাহসিনেশন ব্রো👌,1,entertainment
তোদের দেশ থেকে বাহির করে দেওয়া উচিত। তোরা মুসলিম সমাজের যোগ্য না। তোরা ইউরোপের কোন দেশে চলে যা সেখানে সামনের দুইটা খোলে হাটতে পারবি। তখন তাদের দেশের কুত্তায় তোদের দুধের প্রশংসা করবে।,1,entertainment
প্রভা তোমার দুধ এবং ভোদা সুন্দর নয় কারণ তোমার ভোদা কালো এবং দুধ বেশি বড়। রাজীব তোমাকে চুদে মজা পেয়েছে। তোমার ভোদার সাইজ এত বড় কেন?,1,entertainment
ও একটা মাগি,1,entertainment
বালের কাজ কর,1,entertainment
শবনম ফারিয়া এবং মম এই দুইজন হচ্ছে আন্তর্জাতিক বেয়াদব এবং তার সাথে ওই দাড়িওয়ালা কুত্তার বাচ্চা সে আরো বড় বেয়াদব এবং সাথে আর জন আছে কুত্তার বাচ্চা ওসব প্রতিযোগীদের সাথে যদি আমি থাকতাম চারজনকে ভালো করে ধোয়াইতাম,1,entertainment
কই থেকে ধরে আনছে এইসব আবাল মার্কা বিচারক,1,entertainment
"মাগির বেটি,তার মা বাবা বড় মাদারি চুদ,তারাও মনে হয় মাগি খানা থেকে জন্ম হয়েছে,,,",1,entertainment
তোমারে চোদে শয়তানে মাগি,1,entertainment
ঐ হিজলা কানকী রে পাটক্ষেতে নিয়া যান কেউ 😷,1,entertainment
হেতে আমার হেডার রানা এরা সব গুলা মাধার চুধ মন চাই হেডার পু সব গুলাকে জুতা দিয়ে পিটায়,1,entertainment
ও একটা খানকি মাগি,1,entertainment
ছাগলের মত চেহারা নিয়ে আসছে বিচার করতে নিজেরা মনে হয় কোনোদিন আয়নার সামনে গিয়ে নিজেদের চেহারা দেখেনাই তাই এইরকম আচরণ বিচারকদের পাছায় লাথি মেরে বের করে দেওয়ার দরকার যে পাগলে তাদের কে বিচারক বানাইছে সে হলো একটা রামছাগল,1,entertainment
এ হালার পু হালা কথার সায়োন্ট নাই মেউজি বাজাবি তো নাট দিলি কেন এ হালার পূ হালা কনো বাল তৌ বূজা জায় না,1,entertainment
বিচার চুদানোর আগে ইন্ডিয়ার কিছু রিয়েলিটি শো গুলো দেখে নিশ মাদার চোদ রা তোদে তোদের অভিনয় দেখে যতটুকু শ্রদ্ধা করতাম এখন তোদের শুধু চুদতে মন চাচ্ছে খানকির পোলা মাইয়ারা তোদের গালি দিতে শুরু করলে কমেন্টে শেষ হবেনা😡😡,1,entertainment
তোর চেহারা আর নামের আগে আর ভোদার উপোর কোটি জুতার বাড়ি দিব আমার কাচে আসিস,1,entertainment
সেদিন যদি বঙ্গবন্ধু স্যাটেলাইটে করে চলে যেতাম।তাহলে আজ এই সব আবাল মার্কা বিচারক দেখতে হত না।😂😂😂😂,1,entertainment
এই সব খানিকর পোলাদের জন্য দেশে ছেলে মেয়েদের ভবিষ্যত নষ্ট হয়ে যাচ্ছে। এই সব অশিক্ষিত বিচারকের জন্য দেশের দামাল ছেলেদের ভবিষ্যত নষ্ট। আবার শো এর নাম কে হবে মাসুদ রানা। ওখানকির পোলা নিজের চুল কাটেনা ও অন্যদের হিয়ার কার্টিং নিয়ে অপমান করে। ওর নুনু কেটে নেওয়া হক।,1,entertainment
মাগির গুদে ধোন ঢুকিয়ে দেই।,1,entertainment
পাগল ছাগল এই সব জাজদের গালে জুতা মারা দরকার। ছিরা জুতা মাইরা ব্যবহার শিখানু দরকার এই গাজাখুরদের। গাজা খাইয়া আইসা বসছে চেয়ারে।,1,entertainment
শালার পুতেরা এডি বলে গান। আজকাল ছাগল গরু ও তোদের চেয়ে ভালো গান গায়।,1,entertainment
হালায় বিচারককি হিরোনচি গাঁজা খোর। অয় যখন সোহেল রানা খুজতে বসছে ও নিশ্চিত গাঁজা খাইয়া আইছে। হালার পোলা,1,entertainment
বোকাচোদা তুই মাসুদ রানা সম্পর্কে কিছু জানিস বিবেক থাকলে এভাবে কাওকে অপমান কর। নিজেরা ত পা চেটেচেটে অভিনয় জগতে ঢুকছস আবার ভংচং চোদাও তোগো কারোর জন্মের ঠিক নাই যতসব আচোদার দল,1,entertainment
পভা কেআমার খুব পছন্দের একটা মানুষতোমাকে খুব পছন্দ করিযারা পভা কে খারাপ গালি দেই তাদের মা বাপেরজনমে ঠিক নেইকুকুরের যাত গুলো,1,entertainment
জুতা মারা দরকার পরিচালক জাজ সব গুলোরে বেয়াদবের বাচ্চারা,1,entertainment
মাগির কথাবার্তা শুনলেই গা জ্বলে। ওর কোনো কাজ ই এখন পর্যন্ত রিলিজ হয় নি আর বলে অন্য নায়িকার চেয়ে বেশি জনপ্রিয় এমনকি কাছেই নাই। মাগি আবার হাবিব কে নিয়ে কথা বলে।,1,entertainment
মাসুদ রানা বুকাচুদা।তুমি আমার সাওয়ার বাল মাসুদ রানা খানকিরপো।ভিডিওটা দেখে রাগে সোরিল জোলতিছে।ইচছা মোতোন গালাগালি দিতি মোনে চাছে জানোয়ারগে।সবাই মিলে সো শেসে চোদোন দিবি।,1,entertainment
এই মাগীকে কুত্তা দিয়া চুদাতে হবে,1,entertainment
একটা ছেলেও ঠিকমত বাংলা টা বলতে পারেনা এরা নাকি অভিনয় করবে সব গুলো কে প্রতিবন্ধী আর বালের বিচারক,1,entertainment
কুত্তার চুদা শালারা,1,entertainment
দেশে কি জাজের ঠাটা পরছে এই দরনের জাজ বসাইছে কসাই চুইলাটা তো মনে হয় হাপ পেটিস ফালতু,1,entertainment
গুদে গুদানতর,1,entertainment
তোমার পাছা আমি ফাটাবো!!! শয়তানের বাচ্চা প্রমোট করতে আসছে।।।,1,entertainment
বোকাচোদা দের নিয়ে এসে বিচারক বানাইছে।,1,entertainment
ববি তো একটা ভালো পতিতা,1,entertainment
"জামাইরটা খাইতে পরতে মজাই লাগে,, আর ফষ্টি নষ্টি অন্য বেডার লগে যত্তসব!! নারীজাতির কলঙ্ক এরা...স্বামি বিদেশ থাকলে যদি থাকতে নাই পারছ তাহলে বিদেশি ছেলেকে বিয়ে কেন করছ!! তার ধন-সম্পদ এর লোভে?<br />যাদের স্বামি বাহিরে থাকে তাদের উদ্দেশ্যে বলছি, প্লিজ জামাই ছাড়া থাকতে কষ্ট হলে তাকে নিজের কাছেই রাখুন, সুখে-শান্তিতে থাকুন। তাও দয়া করে নষ্টামি করবেন নাহ।",1,entertainment
যে ছাগলগুলো অডিশনে জাজ করছে তারা সব্যসাচী স্যারও আসলে বাদ দিয়ে দিতো,1,entertainment
"সাকিব একটা মাদারচুত মান্নাকে মেরে প্রমান করে দিলো,টাকার জন্নে সাকিব সব করতে পারে,এটাই প্রমান",1,entertainment
দাঁড়িওয়ালা শালায় একটা মাদারচোদ ওরে কিভাবে বিচারক হিসাবে আনা হলো রাজ বাদে সবার ব্যবহার বাজে।,1,entertainment
এমন আচোদা ভিডিও করার মানে কি আপনারা কি এখন দুধ নিয়ে গবেষণা করা শুরু করতেছেন নাকি মানুষকে এইসব কাজে উৎসাহিত করছেন এধরনের একটা ভালো চ্যানেল থেকে এসব কনটেন্ট কখনও আশা করি নাই এমন বোকাচোদা উপস্থাপিকা আমি জীবনে দেখি নাই উনিও মনে হয় এই অপারেশন টা করাতে চাই বুড়া বয়সে এই দুধ নিয়া যখন সোজা হয়ে দাঁড়াতে পারবি না তখন বুঝবি 😡,1,entertainment
এই ধরনের বেশ্যাকে দয়া করে আর ডাকবেন্না,1,entertainment
সব বিচারকদের জুতা পিঠা করা উচিত দুটা মেয়ে আছে নটির পুরিনতে নাটক করে যে ভাব লইছে যে তারা লাগে নাটক করে মাসুদ রানা এই ছবি বের হলে আমি কখনো দেখাত যাব না,1,entertainment
খানকিরপুত তোদেরকে আমরাই ফেমাস বানাই আর তোরা আমাদেরকে পচাস মাদারচোদেরা,1,entertainment
হায়রে দুধ পাই কই এতো বড় দুধ,1,entertainment
জাজ মিডিয়া নামক কুলাঙ্গার গুলো বাংলা দেশে নিষিদ্ধ করা দরকার এরা সবাই বেশ্যা দিয়ে ছবি তৈরি করে তাও বাবার দেশের নকল,1,entertainment
ভাই করার পর দুধের বোটা গুলো কেমন হইলো যদি একটু দেখানোর সুযোগ করতেন।,1,entertainment
মাদার চুদ হাইওয়ান এভাবে মানূষকে অপমানিত করার অধিকার নেই জানোয়ার বিচারকেরা,1,entertainment
মাগি ব্রা পরছনাই,1,entertainment
জুতা দিয়ে বাভি দিব মাগী,1,entertainment
চোদানির মাগি খানকি তোর দুদ দিয়ে চুদা দরকার কেরিয়ার চুদাও খানকি,1,entertainment
ওই হালায় পগোল হইয়া গেছে গানজ্জা খাইয়া নাটোক বানাইছে,1,entertainment
পাগল চুদিনা😁😁,1,entertainment
সব খানকি দিয়ে দেশের বারোটা বাজিয়ে দিয়েছে এই সব মাগী নিয়ে এসব সো বাদ দেন ভাই,1,entertainment
মানুষের অডিশনে বিচারের দায়িত্বে মানুষকেই রাখা উচিত ছিল। কুকুরকে কেন বিচারকের আসনে বসাতে হবে রে ভাই 🤔🤔🤔 মোস্তফা রাজ😍😍 এবং ফারিয়া😍😍ব্যতীত কোন বিচারককে তো মানুষ বললে ভুল হবে।,1,entertainment
ঔ আবাল গুলাকে কে বিচারোক বানাইচ্ছে,1,entertainment
ওদের পাছাই কে কে কলা গাছ ধুকাতে চান লাইক দিয়ে জানিয়ে দিন,1,entertainment
ঐ সালা ফালতু একটা,1,entertainment
তুই একটা মালাউন,1,entertainment
খানকি বেশ্যা,1,entertainment
তোরা জনই পতিতা তোদের জনমের ঠিক নাই,1,entertainment
আপনারা উত্তেজিত হবেন না সবাইকে সুযোগ দেওয়া হবে কমেন্ট করার জন্য সিরিয়ালে দাড়ান একে একে বিচারকদের হোগা মেরে যান,1,entertainment
তোর মা কে চোদ মাদারচোদ,1,entertainment
কিসব আবাল চোদা নায়ক ঢুকায়.. 😡<br />একজন্য তোদের বালের ছবি কেউ দেখে না,1,entertainment
শাউয়ার পোলা আমার শাউয়ার প্রশ্ন করে এইসব মাগিবাজ পোলাপান রা ইউটিউব ফ্রেমাস হবার জন্য এগুলা করে,1,entertainment
এতো ভালো একটা চ্যানেলের পুটকি মেরে ছেড়ে দিলো কিছু আবালচোদা বিচারক,1,entertainment
বুকাচুদা পরিচালক,1,entertainment
এখানে প্রত্যেকটা ভাইরাই ওই গাবর বিচারকের চেয়ে সুন্দর ছিল।এসব গাদাগুলোরে কেমনে বিচারক আসনে বসতে দেয়া হয়েছে।অংশ গ্রহণ করেছে বলে অপরাধ করছে নাকি।যতসব পাগলছাগল বিচারক। খুব রাগ হচ্ছে এতো অপমান মানুষ মানুষকে করতে পারে।আয়নায় নিজের মুখ কখনো দেখছেনি এই বলদগুলা,1,entertainment
দুরো মাগি চিটিং,1,entertainment
সব হলো মাগি চুদার দালাল,1,entertainment
কেও নিজেকে হিরো মনে করেনা মাগি কোথাকার,1,entertainment
ভাই শালাদের পাছায় লাথি মারা উচিৎ। এরা নাকি বিচারক। 😒এরা সবগুলোই বাইনচোদদদদদদদদদদদদদদদদ😡,1,entertainment
মাগির থেকেও খারাপ,1,entertainment
বানচোদ বিচারক জুতা মার,1,entertainment
খানকি ভারা দিয়ে দুধ বানাইছা। রাস্তার ছেলেরা তো দুধ দেখে বাঝে কমান্ড কর। তরে বিয়ে করবে তার ধন পচে যাবে আর হাবিব তরে বিয়ে করবে। ভালই পচাইছে জয় ভাই,1,entertainment
ওর মাথার কাপর নেই কেন<br />অন্য যায়গায় মাগি বাজি করে তা বাদ কিন্তু <br />আরবি পরতেছে মাথায় কাপর নেই আর উচ্চারণ ফাযলামো নাকি,1,entertainment
ডায়রেক্টর এর পুটকি মারি।।।মাদারচোদ ফিনিশিং দিতে পারোস না?বাল বানাইছোস?তোরে আরও গালি দিতাম দিলাম না।আমার চ্যানেলে যা পুরা বিনোদন পাবি।,1,entertainment
পুরা বেয়াদপ।এই খানকি পোলাগলে দইরা চুতা মারা দরকার,1,entertainment
তোদের পুটকির ভিতরে মূলা ভইরা দিমু জানোয়ারের বাচ্চা,1,entertainment
আমার মনে হয় এর জন্ম পতিতালয়ে । কারণ সে জাহান্নমে যাবে ।,1,entertainment
পরিচালক. একজন মাদারি,1,entertainment
এই রকম কিছু মাগী আছে,1,entertainment
ভাই ঐ হালা দুইটারে কিছু খওয়ার নাই ওরা তো কুত্তার বাচ্চা। কিন্তু মম আর ফারিয়ার চরিত্র নাটকে দেখেচি। বাস্তবে যে ওরা পতিতা থেকে ওঠে এসেছে যানতাম না এটা আজকে জানলাম। ওদের বাস্তব ব্যবহারের মাধ্যমে।,1,entertainment
পরিচালক একটা নাস্তিক<br />তাইতো এই ভাবে <br />নাটকটা পরিচালনা করছে।<br />Sorry Only for this drama ok.<br />don&#39;t mind. This drama is not good.,1,entertainment
বদমাইশ ছেরি,1,entertainment
মুর্খচুদা টা মাগি এইখানে যেই ভাব নিছে😠😠😠 এই মাগিদের কে চুদে চুদে মেরে ফেলা উচিৎ😠😠😠😠 আর বাঞ্চুদ টা রে কুত্তা দিয়া চুদানো উচিৎ,1,entertainment
"সব দোষ ছেলেদের কারন, যদি বিয়েই করতে হয় তাইলে বিদেশ থেকে আশার পর কর,আর যদি বিদেশই যাওয়া লাগে তাইলে বিয়া করার কি দরকার।। মাদারচোদ ছেলেরা বিয়ে করে বিদেশ যাবা,আর বউ পরকীয়া করলে দোষ",1,entertainment
তুই তো মাগী তোর পরিবার নেই,1,entertainment
ছোট্ট মেয়ে টা কখন জে মাগি হয়ে গেলো কিছু জে বুঝলাম না,1,entertainment
আমি যৌনাংগ দেখতে চাই,1,entertainment
মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির মাগির ঘড়ের মাগি তুই সানাই মাগি,1,entertainment
পাগল মানুষকে নিয়ে আরো কত কিছু দেখতে হবে???<br />👇📚📚📚📚📚📚👇,1,entertainment
দাড়িওয়ালা মাদারচোদ টা কে তর যোগ্যতা আছে মাসুদ রানা হবার আবার বিচারক হবার আইছে,1,entertainment
শাকিব খান ছাড়া কে হবে মাসুদ রানা ছবি মুক্তি পেলে কুত্তাগুলো সিনেমা হলে গিয়ে দেখবে না আর আমার মত কোটি সাকিব ভক্ত সিনেমাহলের মুখে প্রসাব করে দিবে দেবে আগে আমি বাংলা মুভি ছাড়া কোন মুভি দেখতাম না আর এখন বাংলা মুভি দেখলে আগে দুইবার থুতু দিয়ে চলে যায় মাঝে মাঝে সাকিবের কিছু মুভি দেখি সাকিব ভাইয়ের অন্যসব নায়কের মুভি মুখে প্রসাব করে দেয়,1,entertainment
"এই হিজলা নায়ক হলো কেমনে বালের ছবি,",1,entertainment
সারা জীবন জানতাম বয়ফ্রেনড বা শামি কে ধোরে রাখতে মোন আর ভালোবাসা লাগে।আর এখন এই মাগি টা বলে। কি আর বলি।আসলে ভাসা নাই। আরো বড়ো করো ছোট হোয়ে গেছে। জা আজ় কোরে মানুষ ভুলাইতেছো।মরনের পর সাপ কুড়ে কুড়ে খাবে মজা টা তখন বুজবি।ছি ছি ছি।,1,entertainment
নিপুন কি নিজেকে <br />১৫বছরের কচি মাল মনে করে নাকি?,1,entertainment
এই সব মাগী চোদা ছবি বাদ দাও।এটা কি পরিচালক না গাধা,1,entertainment
শালা বিচারক গো গোয়া মারা দরকার। সবাই কি একমত,1,entertainment
কুত্তার বাচ্চা তোদের সবগুলার জুতা দিয়ে মারা উচিত,1,entertainment
বেডা তর চুলইত পাকাইছস রঙ দিয়ে অন্ন ছেলেরে আবার কস কেন চুল লাল করছে কেন আবাল বুইরা🙄🙄,1,entertainment
পরিচালক গাঞ্জা খেয়ে বাল লেখছে।,1,entertainment
ওরে গরু দিয়ে চ লাগবে বোদা ফাঁক হয়ে গেছে,1,entertainment
বিচারক খানকির পোলা এদের জন্মের ঠিক নাই,1,entertainment
হালায় দুদু ধরে কে,1,entertainment
ফেমাস হবার জন্য এত কিছু তুই সালি রাস্তাই যত চায়ের দকান আছে তাদের কাছে গিয়া বিক্রি কর তাতে টাকা পাবি আর সাদারন লোক অন্ন রকম সাদ পাবে তাতে তুই আরো বাইরাল হবি,1,entertainment
সব কয়টা বিচারকদের চোদার দরকার 😠😠😠😠😈😈😈😡,1,entertainment
বিচারক গুলার নাই কোন যোগ্যতা নাই কোন ভদ্রতা সব গুলা আবাল। জুতা পেটা করে বের করে দেয়া উচিত,1,entertainment
এই কুত্তারবাচ্চা গুলোকে বিচারকের আসনে বসাইছে কোন বেয়াদবের বাচ্চারা,1,entertainment
এতো প্রশংসা করার কিছু নাই হিজড়াদের দ্বারা কোন কিছুই সম্ভব না দেখতে অনেক স্মার্ট হলে কি হবে বউ রাখার মতো যোগ্যতা ওর নাই,1,entertainment
অর ছেহারা দেখ লে মনে হয় খানকি মাগী,1,entertainment
হেডার নাটক/শালার পরিচালক গান্জা বাবা খায় নাহি????,1,entertainment
তোর মতো বেয়াদব আমার দরকার ছিল শালী আমার হাত পাওবাইনদা কাম করতাম জালিম,1,entertainment
সব কয়টা বিচারক মাদারচোদ কি বাল জানে মাসুদ রানা সম্পর্কে,1,entertainment
শবনাম আপ্পির সাতে ছেলেটা মনে হয় বাবা খোর মাদার চুদ কিভাবে মানুষের সাতে কথা বলতে মাদার চুদ জানেনা 😊,1,entertainment
চুতমারানি তোই জাতির জন্ম অপমান,1,entertainment
মাগি তোরে যদি পাইতাম🤔,1,entertainment
শালা শয়তানের কারখানা,1,entertainment
3 টি প্রেম করছে হা হা .যারা মিডিয়াতে কাজ করে মিনিমাম ৩০ টা সুনা ভিতরে গেছে .আর মিথিলাকে তাহসান করে দিতো না আর এইটা নিয়েই ওদের মদদে ভেজাল .আর একারণেই মিথিলা ভোদার রস চাটার জন্য চাটার রুগী খুঁজে,1,entertainment
জোরে চোদা দাও।,1,entertainment
তোকে চোদবো কত টাকা নিবি এক রাতে জান আমাকে,1,entertainment
মনডা কি জে করতে চায় খানকির পোলা আর খানকিরে,1,entertainment
মাগির দুধ কে টিপলো আর এতো বড়ো বানালো কে,1,entertainment
বিচারক কে লাগে গরু চুলের মত শালা পালতু বিচারক সবাই,1,entertainment
তোর গফ কি ভারজিন তুই তো খাইয়্যা দিছোছ আবার আরেক মাইয়্যারে নিয়া ট্রল ভিডিও বানাছ মাদার চোদ তোর মা কি ভারছিন ছিল তোরে তো আফ্রিদি ও দেখতে পারে না আজকে থেকে তুই আমার ও শত্রু মাদার চোদ।,1,entertainment
শবনম পাদিয়া বুড়িচোদা ইঞ্চি মেক আপ লাগানো পাব্লিকটা নাকি ফকিন্নি বস্তিগুলার ক্রাশ😂😂😁 তোগো যাগো ক্রাস এই পাদিয়া উলটা হইয়া নিজের পুটকিটা দেখিস ওইটা আরো সুন্দর 😂😂😂,1,entertainment
ওরে হালার পো হালারা নাটক বাস্তবের মিলাইয়া দিছে,1,entertainment
গত কিছুদিন আগে আমাদের পাশের বাড়িতে একটি গাভী বাচ্চা প্রসব করেতে গিয়ে মারা গেছে৷ তোহ বাছুরটার জন্য এই বৈশ্যারে আনলে ভাল হবে৷,1,entertainment
সালাদের একটাকেও যদি সামনে পাই জুতা দিয়ে পিটাব থু,1,entertainment
মাগি নিয়ে বালের মজা কানকির পোলক,1,entertainment
এরা বিচারক বাইনচোদ মার্কা লোক যে কত প্রকার হতে পারে তা আজ দেখলাম এক হাজার টা গালি দিতে মন চাচ্ছে।,1,entertainment
সালা সালিদের জুতার মালা উপহার দেও ভাই।।,1,entertainment
সব গুলো গাধার বাচ্চা কম্পিটিশনে গেছে আর শুয়োরের বাচ্চারা জাজ হয়েছে,1,entertainment
শালারে বাংলাদেশ থেকে গার দরে বাহির করা হোক,1,entertainment
বিচারক মাদারচুদ কে জুতা পিঠা করার দরকার,1,entertainment
এইসব ছাগলকে বিচারক বানিয়ে পুরো অনুষ্ঠানকে কলংখিত করা হয়েছে,1,entertainment
আবে হালায় মাসুদ রানাটা কে আর জাজরা সব ছাগলের ঘরে ছাগল,1,entertainment
এই মাগি ওর ভুদা ভারা দিয়ে দুধ বড় করছে।,1,entertainment
পরিমনি গোয়া মারা খুব দরকার অর দুধ বড় বড় এজন্য গোয়া মারা খুব প্রয়োজন।,1,entertainment
বাংলিশ কুত্তা বাচ্চা বাংলায় ভালো করে বলতে জানে নাহ আবার ইংলিশ মারা,1,entertainment
এই আবাল গুলোকে ধরে রাস্তার মধ্যে দাঁড়িয়ে জুতা দিয়ে পিটানো উচিত,1,entertainment
ভিডিওটি দেখে মনে হচ্ছিল এই সব বিচারকদের কাছে পাইলে জুতা দিয়ে বাইয়ায়া কপালের চারা খুলে ফেলবো শালা 😠🖕,1,entertainment
মম মাগি কয় কী কোন পতিতালয় থেকে আসছির রে ফারিয়া মাগি রে তো ভালই মনে করতাম,1,entertainment
তুমি মাগিহাবিবের বউ ছিল এর পর ও কেন ওর সাথে লটর পটর করলা,1,entertainment
আমার বালের বিচারক এগুলো ওদের একেকটা কে ধরে থাপরানো উচিত,1,entertainment
দাড়ি অয়ালা টা আচোদা,1,entertainment
তোমার ভুদা দেখে অনেক হাত মারছি,1,entertainment
মাসুদ রানা কোথাকার বাড়ার বাল,1,entertainment
তোমাদের লংটা ছবি কেও আর দেখে না শালার মাগিদের নিয়া ছবি করে বাংলা,1,entertainment
প্রথমে ক্ষমা চাই আপনাদের কাছে যারা আমরা মত কমেন্ট পড়তে আসেন। কারণ আমি গালি দেব এসব পাগল বিচারকদের এবং যারা এদের বিচারক বানিয়েছেন তাদের। আমার বাড়ি চট্টগ্রামে চট্টগ্রামের ভাষায় পাগলদের জন্য একটা এসপেশাল গালি আছে সেটা হল পলেরে ছুদিয়েরে পানিত ফেলা পানিত নফেলাইলি পলে মাইনশিরে কইবো ইতে আঁরে ছুদি দিইয়ে ছুদি দিইয়ে। আর পানিত ফেলাইলি ছুদি দিইয়ে কইতোনো পরে কইবো ইতে আঁরে পানিত ফেলাই দিইয়ে। এর অর্থ পাগলকে ছুদে পানিতে পেলে দাও। পাগল মানুষকে বলবে আমাকে পানিতে ফেলে দিয়েছে ছুদে দিছে বলবে না। এসব বিচারক পাগলাদের ছুদে পানিতে ফেলে দেয়া দরকার।,1,entertainment
এই চোদনার বালটা কেটা ভাই,1,entertainment
ওরে সংরক্ষিত আসনের এমপির বাড়ির কুত্তা দিয়ে চোদানো হোক,1,entertainment
ওরা বিচারকের যোগ্য না। ওদের এক এক করে খারা চোদন দাও।,1,entertainment
হালার চুল দাড়ির যা হাল না জানি অন্য জায়গার কি অবস্থা,1,entertainment
হাসতে হাসতে পেট ব্যথা হয়ে গেছে মিথিলা ভার্জিন এখনো এক সপ্তাহে বউ তামা তামা হয়ে যায় এগারো বছর সংসার করার পর এখনো ভার্জিন কি পরিমাণ গাঁজা সেবন করলে সৃজিত এই কথা বলতে পারে আপনারাই বলেন,1,entertainment
ওরে সরবোনাশ কঠিণ বডিতো নুসরাতরে তুই মরলে তর গোয়াদিয়া দিবো ডামবেল!খোদার গজব পরুক এই সব বেশ্যাদের উপর!,1,entertainment
তোর হেডা,1,entertainment
এই গুলো ভাই মাগী আর মাগীর দালাল এই গুলোরে সারা দিন বাঁশ দিলেও যে না দিলেও তাও।,1,entertainment
তুরে পেতনির মত লাগে।আর তুর মত পাগল কেউ নাই,1,entertainment
তোরে চুদদে সাগর খবর,1,entertainment
সব গুলা জাজ খানকির পোলা,1,entertainment
"বাংলাদেশে ১.৫ কোটি প্রবাসীর বউ পরকীয়া করে,,,,,এদের কেউ খারাফ বলে না,,,কারন এরা মুখোশ দারী..<br /><br />সব দোষ যেন পতিতার,,,,<br /><br />প্রবাসীর বউরা বড় পতিতা।।<br /><br />👌যারা পেটের দায়ে পতিতা হয়,,,তাদের কোন দোষ নাই",1,entertainment
এইসব বিচারকদের পতিতাদের বিচারক হওয়ার ট্যালেন্ট আছে। মেয়ে বিচারক বোদার যোগ্যতায় এ ই চেহার পাইছে।আর ছেলে বিচারকরা বউকে ভাড়া দিছে নয়তোবা গার্লফ্রেন্ডের বোদা ভাড়া দিছে।,1,entertainment
মাগীরে বাঁশ দিয়া করা দরকার মিল্ক ভাইরাস।,1,entertainment
সালারে মিনিট পিটাতে পারতাম সালিরে মিনিট চুদে পারতাম,1,entertainment
হতেই পারে কারন সৃজিতের ধন হয়তো মোটা এবং বড় তাই হয়তো ওর ধন ঢুকে নি,1,entertainment
মাগিরে লেংটা কইরা চুদছে জিত,1,entertainment
এক নম্বর মাগি,1,entertainment
এই পতিতাকে সবাই না বলুন,1,entertainment
কথা বার্তা নরমাল ভাবে বললে কি হয় ভাউ এরকম কেমন বোধ করচ্চচ্চচেন টাইপ কথা বলে কি বুঝান।এটা যে চরম বিরক্তিকর লাগে সেটা কি জানেন। বাইরের দেশের অনেক শো দেখি কই তারাতো এরকম বলেনা। আর কিছু কিছু শোতে দেখলাম ডিরেক্ট গরু ছাগলের মত প্রশ্ন কথাবার্তা। বাইরের দেশের গুলো দেখে অন্তত শেখেন। নায়িকা কেমন লাগে চুদতে কেমন এরকম টা ছাড়া কি আর কিছুই নাই,1,entertainment
এই মাদার চুদেরা আমাদের বদনাম করে নাটক চুদাই দোনের নাটক করচে খানকির চেলেরা,1,entertainment
ছি ছি ছি দিকার যানাই তোকে যে তুই একটি নারী বলে । তোকে নারী না বানিয়ে মেয়ে কুকুর বানানো উচিত হোতো ।তাহলে তোর জন্য আরো ভালো হতো ।,1,entertainment
বিচারক এর আসনে এই বান্দর টারে কে বসাইছে,1,entertainment
কই একটা বিচারক ছাড়া আর সব গুলা পালতু।।এরা এত খারাপ আচরন না করলে পারে।।পকিন্নি কাজ কারবার।।।আবালচোদা,1,entertainment
অরে মাগিরে,1,entertainment
মাগির পুলারা এটাকি ছবি না আর কোনো,1,entertainment
এই বিচারক নামের গরু ছাগলগুলোরে কোন জঙ্গল থেকে ধরে আনলো জুতা পেটা করা হোক।,1,entertainment
সাংবাদিকদের কাম কাজ নাই 😠 সালারা আর কোন পথ খুঁজে পায় না🤔 আসছে মাগিদের চিপা চাপা দেখাই তে !,1,entertainment
লুচ্চা ফাহিম কি করে এখানে ওরে লাথি মাইরা বার করো,1,entertainment
সাবিলায় একটা খানকি 😂,1,entertainment
খানকির পোলা রা এইটা নাইচ মুভি তোরা পোলাপাইন মানুষ কি আর কবি হালার পুতেরা এই রকম ছবি তোরা মা বোন কে নিয়ে দখচ,1,entertainment
বালের মতো তর মুখটা।,1,entertainment
দাড়িওয়ালা সব চেয়ে বড় মাদারচোদ সাথে ফারিয়া মম কম খানকি না 😡😡😡,1,entertainment
এই কুত্তার বাচ্চা কে কোন শালা জাজ বানাইছে,1,entertainment
খানকির বাচ্চা তোরে এনাকোন্ডা দিয়ে মারা খা,1,entertainment
এ কুত্তার বাচ্চা মানুষকে অপমান করছে কুত্তার বাচ্চাকে মাসুদ রানার বিচারকের চেয়ারে বসে থেকে যে বসে আছে সে একটা মানুষের বাচ্চা নাএ শুয়োরের বাচ্চাকে এখানটা উট করতে হবে ঘন্টার মধ্যে আউট করতে হবে শালা শুয়ারের বাচ্চারা ঠিকমতন বিচারক প্রতারণা শুয়োরের বাচ্চা মানুষকে অপমান করা হয়েছে,1,entertainment
ওরে কুত্তা ও করবেনা আচোদা,1,entertainment
এ অনুষ্ঠানে এখানে বন্ধ করার অনুরোধ রইলো সব মাদারচোদ পরিচালক আমার সাথে কে কে একমত লাইক দিন,1,entertainment
মাদারিচুদরা অডিশন কিবাব নে শেইটাও জানে না,1,entertainment
তোর মত মাগির কথা শয়তান চারা কেউ সুনবেনা শয়তান মাগি,1,entertainment
শালার ঘরের শালারা মনে হয় বাবাখোর গাঁজাখোর গাঞ্জুট্টি কুত্তার বাচ্চা কিভাবে বিচারক হয়,1,entertainment
জাজ ফাহমিরে পাচায় লাত্তি দিয়ে এখান থেকে বের করে দেওয়া উচিত।,1,entertainment
আবাল ২ টা আবাল বাড়ি কইতরার আাবাল আসিফ ইজ রিয়েল হিরো,1,entertainment
বিচারক গুলো বাপের আগে বাল ফালানি শুরু করছে,1,entertainment
চুদির বেটা বালের সিনেমা,1,entertainment
কতগুলো কুকুরের বাচ্চা বিচারক হইছে ছি,1,entertainment
ভাই এই মাগিরে চুদতে কত টাকা লাগে,1,entertainment
পুরান পাগলের ভাত নাই নতুন পগলে আমদানী এমপি হয়ে কি করভো সানাই মানুষকে ধুত খাইভো,1,entertainment
মাগী চুদদে দিবি,1,entertainment
সব চোর গুলারে বিচারক বানিয়েছে মাদার চোদের বাচ্চারা । সবনম ফারিয়া আর মম তরা না অভিনয় করছ তোদের কথার বাসা কেন এরকম । বেশ্যা মাগিরা তরা আবাসিক হোটেলে গিয়ে বস । তরা আবাসিক হোটেলের যুগ্ম মাগিরা । বাসা শিখ । আর সবনম ফারিয়ার সাথে যে বসেছে সালা আবাল তার চুলের স্টাইলটা দেখলে মনে হয় সে ভিক্ষা করতে এসেছে । এদের কে বিচারক না বানিয়ে মাঠে নিয়ে গরুর হাল চাষ করালে ভালো হবে। সালা আবালের বাচ্চারা,1,entertainment
তুমি চুদা দেও আর ওরা এইটা করে না তাই সবাই তোকে চিনে না তুই জে কী অবিনয় করস বুজি না জাতির জাননো বাষন দিতেসে শুনেন,1,entertainment
আই তোরে চুদি,1,entertainment
এইসব আবাল দের কে বিচারক বানাইসে তোদের আছে বাল চুদ। তোদের চেহারা নিজেরা দেখে নে তোদের কেমন দেখায় তারপর অন্নকে করিস,1,entertainment
শবনম ফারিয়া তরে বাশ দিমু গুয়া দিয়া বুজতে পারলি মাগি।আর মম তরে ও দিমু।,1,entertainment
নিজের দেশের সংস্কৃতি নিজেরাই ধ্বংস করছি। বিদেশী সংস্কৃতির প্রতি নির্ভর হচ্ছি। সত্যি বলতে একমাত্র মঞ্চের শিল্পীরাই সেরা।মনে রাখা উচিত যে কোন খারাপ কাজে প্রবেশ করায় শয়তান এবং এটাও সত্যি যে ঐ শয়তানই আবার কিছু প্রমাণ রেখে দেয়। যাতে করে পরবর্তীতে বিপদে পড়তে সহজ হয়। এক্ষেত্রে পরিচালক আবাল হচ্ছে মুর্খ যদি মিথিলা তার বউ হয় তাহলে তারা কি করছে তা ছবি বা ভিডিও করার প্রয়োজন কী? এজন্যই শয়তান সুযোজ পেয়ে যায়।আমার কথাগুলো খারাপ লাগতে পারে সবার কাছে দুঃখিত।,1,entertainment
মৌ তুই আমার বালের অভিনেতী,1,entertainment
"মিথিলা বার্জিন হলে বাচ্ছা কি পুটকি দিয়া বাহির হয়েছে,ঐ মাদার চোদ বার্জিন কি বুঝে,,মিথিলার বোদায় হাতির ধন ডুকানো দরকার?",1,entertainment
সানিতার সাথে আমি চোদা চুদি খেলবো,1,entertainment
।চুপ কর শালার পুতেরা।। এই মাগির বাচ্চা গুলাকে কে জাজ করচে।। মানুষের সাথে কি ভাবে কথা বলে সেটাই তো জানেনা এরা । কি করে এরা মড়েল হইচে ছিঃ।।।। মমকে ভালো জানতাম খুব ভালো লাগতো কিন্তু এখানে এইসব অহংকারি কথা শুনে তো থুথু দিতে ইচ্চে করচে। ফাউল।। আর কাকের বাসা জঙ্লি টা নিজেকে কি মনে করে । হিরো আলমের চেয়েও তো অদম ও। পাগলের মত,1,entertainment
বিচারখ তো বালপাক না,1,entertainment
তরে চুতলে খুব মজা পাইবো খানকি ময়ে,1,entertainment
",বাল ছেড়া নাটক।মাদারচুদ",1,entertainment
পাবনার পাগল ও তার থেকে ভালো,1,entertainment
মিসা লুচ্চারে পাইলে একটা জুতা দিয়ে পিটিয়ে দিতাম,1,entertainment
তোগো গোয়ায় বাশ ঢুকাবো তোগো গোয়ায় বাশ ঢুকাবো তোগো গোয়ায় বাশ ঢুকাবো হালার পুতেরা,1,entertainment
ছাগল ইফতেখার ফাহমিকে সবচেয়ে বেশি ভরার কথা ছিলো অথচ তাকে ভাই বানিয়ে তার প্রতি আপনি সদয় ছিলেন। ছাগলটা হিট দু একটা নাটক বানিয়েছে তো কী এমন করছে! কারো প্রতি স্বদয় আবার কারো নির্দয় এসব স্বজনপ্রীতির আওতায় পড়ে বুঝলেন।,1,entertainment
লুচ্চা সাহতাজ মাগি কাপড় ঠিক কর,1,entertainment
কুত্তার বাচ্চা একটা সমাজ নষ্ট করছে শালী। ওর মা বাবা কি করে,1,entertainment
অস্থির হইছে ভাই কুত্তার বাচ্চারা যেভাবে পোলা গুলারে অপমান করছে আমি থাকলে ওগো জুতা দা বাড়িতে জায়গায় দাড়ায়,1,entertainment
মাগির হট দেখতে চাইলে চোখ রাখুন,1,entertainment
তারেকের ইচ্ছা পূরন হইছে মাগীর পোলা য় দেশের নেতা না হইয়া চোর ও সন্ত্রাসী হইছে।,1,entertainment
আমাদের আইঞ্চলিক ভাষায় একটা কথা আছে কম পানবর মাছ যদি বেশী পানিত পরলে চাটাচাটি করে শালারা কম পানির মাছ,1,entertainment
নায়িকার অভিনয় শেখ হাসিনার মত ডাইনি,1,entertainment
তোরে ঘোরার সোনা দিয়ে চুদা দেওয়া যেতো তাহলে ভুজতি,1,entertainment
মাদারচুদরা ছবির চেইন কাটলে ছবি আপলোড দিবি না।,1,entertainment
লালনরে শাই পুটকি মারছে,1,entertainment
বিচারক ফালতু শালারা,1,entertainment
পরিচালক একটা কুকুরের বাচ্চা। নাস্তিক। ইসলাম ধর্মের অপমান করছে।শূয়রের বাচ্চা,1,entertainment
এমন বাইঞ্চোদ মারকা গান আমার লাইফে সুনি নি। ফালতু আবাল চোদারা আর লিরিকস খুইজা পাইলো না। সব আবালের দল গাঞ্জা খোরের দল।,1,entertainment
হালার ঘরে হালা তোরা যে বিচার করো তো করতে পারিনা,1,entertainment
বালের গান বালের শিল্পী,1,entertainment
এই হালারা এই ছবির গানগুলো দে,1,entertainment
সালারা কি বুজে এদের কে বিচারক দিছে।সব সালাই আবাল,1,entertainment
গুয়ে গুয়ে গন্ধ ছড়ায়ে ফেলছে ফাহগু রাগু মগু ফারিগু,1,entertainment
ছেলে দুটাই মাদারচুদ। যেই খানকির পোলায় কইছিলো এখান থেকে এক দৌড় দিয়ে চলে যাও খানকির পোলা তর মাইরে চুদি,1,entertainment
সনিতার চেয়ে সনিতা দুধ বড়,1,entertainment
জাজ রা ছিলো এক একটা মাদারচোদ ওরা মানুষ কে মানুষ মনে করে না খানকির পোলারা ওদের যে ভাবে ওপমান করলো সত্তি আমি অভাগ হোলাম ভারিয়া আপু ও এটা ভালো করে নাই আমি কি কউকে গালি দিয়েছি,1,entertainment
রানা কে জনি সীন মোমো ফারিয়াকে সিফাত কাকার জার্মান শেফার্ড ফামি কে ভাদ্র মাসের দেশি কুত্তা দিয়ে কে কে চুদাতে রাজি 👍👍👍👍👍👍👍 দেন।,1,entertainment
তোমার বড় বড় দুধ দেখে ভয় লাগে,1,entertainment
বাহ্ চুদির ভাই বাহ্ কি সুন্দর করে গানেরে চুইদ্দা দিলা।।,1,entertainment
ফারিয়া খানকি মাগি।তার মারে চুদি,1,entertainment
এই দাড়িওয়ালা বোকচোদটা চশমা পড়ে আছে কেন,1,entertainment
এই শুয়ার গুলা বিচারক হওয়ার কোন যোগ্যতা রাখেনা পর্নোগ্রাফি মুভির ডিরেক্টর হতে পারবে।,1,entertainment
যারা কমেন্ট করেছে তাদের উদ্যেশে বলছি ভাই আর বোনেরা তোরা সালা কাঠি করতেই জন্মেছিস কোনোদিন কিছু করতে তো পারবি না কিন্তু কেউ কিছু করতে চাইলে তাকেও গাল দিয়ে ঘর ঢুকিয়ে দিবি।,1,entertainment
মৌসুমির দুধ এতো বড় কেনো,1,entertainment
আপনারা দেশে আর মানুষ পান না এ রকম খানকিদের ছাড়া।,1,entertainment
এ ই মাগি তোর ভুদায় বাল আছে,1,entertainment
সালাদের কে বানাইছে বিচারক😡😡,1,entertainment
"খনিকের পোলারা,জোরে দিস",1,entertainment
মাগির বুক ওনেক বড়,1,entertainment
বিচারক সালায় বলদ লগে একটা বলদি,1,entertainment
"শালার পুত পরিচালক বালের নাটক বানাইছে,ছেলের বদলে অন্যের মেয়েকে দিতে বলে।",1,entertainment
উপস্থাপকঃ ভাইয়া আপনাকে অনেক অনেক ধন্যবাদ এই ধরনের বেয়াদবদের কে এভাবে অপমান করা দরকার আপনি অপমান করলেন উনি তো একটুও বোধ করলেন না যে উনি অপমান হইছে ওনাদের স্থান পতিতালয় হওয়া উত্তম ফালতু লোক কেন আপনারা মিডিয়ার সামনে নিয়ে আসেন যাদের কোন লাজ লজ্জা শরম ইয়া জ্ঞান বোধ কোন কিছু নেই তারা কেন আপনাদের মিডিয়ায় আসে আপনার কথা গুলো অনেক ভালো লাগছে ভাইয়া আপনাকে অনেক অনেক ধন্যবাদ,1,entertainment
মাগী বাজির আর জায়গা পাও না খুজে কতো গুলো চোদানির পোলা আর পতিতা নিয়া আসছে 😠😠😠,1,entertainment
কুত্তার বাচ্ছা গো হাতের কাছে পেলে,1,entertainment
ভাই তুমার মেয়ে কে খাংকি মেয়ের কাছে যেতে দিবে না।,1,entertainment
বেইশা মাগী,1,entertainment
কি সব বালের বিচারক নিজেই কথা বলতে পারে না ওই আবার বিচারকক,1,entertainment
ধোনের নাটক। খানকির পোলা।,1,entertainment
মাদার চুদেরা মানুষকে তদের জখার মনে হয় আশা সবাই করতে পারে জজের আচার আচারন ভালনা,1,entertainment
এ হালায় পাক্কা বিড়ি খোর,1,entertainment
"সানিতা দুধ কত বড় , আরবি মহিলার দুধু এত বড় না,সানিতার নেকেট বের হবে বেশি দেরি নাই , সানিতার দুধ কে খাবেন",1,entertainment
একে ৫০ টাকা দিলে চুদা যায়,1,entertainment
তুই এম পি না হয়ে চোদা খাওয়ার জন্য ভাড়া যা ।,1,entertainment
কুত্তার মতো চেহেরা,1,entertainment
চে দাচুদি,1,entertainment
খানকির পোলা বিচারক গাজাগোর তুই তো চুল বাল কাটস না আরেক জন কে নিয়ে মজা করস মাদারচোদ,1,entertainment
খানকি মাগি লাখ সামান্য তাইনা সালি এই টাকা তোর দুদ বরো না করে গরিব মানুষদের দান করতি আরো বেসি পাব্লিসি পেতি,1,entertainment
তুই কেবলই তার দুইটা হনুমান কে নিয়ে বিচারকের আসনে বসে কি পাগল,1,entertainment
সবনরম ফাইরালারে দেখলে মন চায় ধনটা মুখে রাখি ওর,1,entertainment
এই সব মাগীরার কারনে আজ বাংলার মা বোনেরা অবহেলিত,1,entertainment
কে হবে বাল রানা,1,entertainment
এক একটা খান্কি মাগির পোলা বিচারক হইছোস মাদারচোদের বাচ্চা গুলা তোদের নাটক আর কোন সময় দেখবো না,1,entertainment
শাহরিয়ার নাজিম ভাই খানকি নিয়া শো বন্ধ করুন,1,entertainment
ভাই রংপুরের মেয়েরা নটি পারার নটি এরা দুধ বর করে ব্যাবসা করে,1,entertainment
বালের মুভি বানায় হালার পুলারা,1,entertainment
ওও কি কচ্চে 🤔🤔 শালির বেটি পকানের নিচে একটা থাপ্পর মারবো আজীবন এর মত ঝিরঝির করবি 😎😎,1,entertainment
মাগি সানাই তোর দুধ কি বড় কি করে,1,entertainment
১৮ কোটির চোদা খাওয়া শেষে এখন ১৫০কোটির চোদা খাবে মিথিলা,1,entertainment
শালা গানকাটা কেন বানচুদ,1,entertainment
পরিচালক গাজা খাই বানাইছে।,1,entertainment
একটাকেও বিচারকের মত লাগতাছে না কুত্তা গুলা,1,entertainment
তোরা আবাল,1,entertainment
বোকা চোদা,1,entertainment
বালের সাউন্ড দিছোস হালারা। দুনিয়াতে আর সাউন্ড খুজে পাস না,1,entertainment
শালার পুতেরা তদের কি কাজ নাই,1,entertainment
মাদারচুত সালারা,1,entertainment
অাবাল মার্কা বিচারক অাহা চ্যানেল অাই এগুলারে কোথাথেকে ভের করচেন । যতসব অাবাল 😡😡,1,entertainment
শালা ছাগলের বাচ্চা মাদার টেক এদের যাত্রা থামাতেই হবে,1,entertainment
বালের জাজ সব ভদ্রতা জানে না,1,entertainment
তাকে জাতীয় মাগির পদক দেওয়া হোক,1,entertainment
এক পতিতা আরেক পতিতার সাক্ষাতকার নিচ্ছে,1,entertainment
ওর মা নটি বিদায় ও নটি হয়েছে ওরে কুকুর ও করবো না,1,entertainment
আবাল মার্কা নায়ক একটার কারণে মুভিটাই শেষ,1,entertainment
নারী কস কেন মাগি,1,entertainment
কি চ্যাটের গান শালার,1,entertainment
এই খানকির পুলারা আর টাকার মাগিরা বিচারক হয় কেমনে ঘা জলতাছে জীবনে যদি একদিন পাই জুতা দিয়া মুখে মারমু কামলাচুদারা,1,entertainment
কোন বাইনচুদ এ এই গান বানাইছে আমারে কেউ মাইরালা 😂😂😂😂,1,entertainment
এদের নাটক সিনেমার গুষ্টি চুদি । চুদির ভাই সেলুন দিতে চাই,1,entertainment
নাটকির পুতেরা এত ভালো বুঝো তাহলে তোরাই নায়ক হয়ে যায় মানুষগুলো হস্তনস্ত কসকা,1,entertainment
হালা নিজের চুল দাড়ির ঠিক নাই অন্যর কাটিং বিচার করিস বাল চোদা বিচারক।,1,entertainment
দারির কোনো ধোস নাই কিণ্ডু বিচারক দিলো এমন চার কুকুরকে অামার অনেক কষ্ট হয় বোদার মাসুদ রানা ওকে,1,entertainment
একটা দেশের অভিনেতা অভিনেত্রী তথা সেলিব্রেটি গুলার আচার আচরন হবে অনুকরণীয়! মনে হচ্ছে এদেরকে মাটি কাটার জন্য নিয়ে আসছে। যত তারাতারি চুক্তি কাজ শেষ করে টাকা পাবে ততই মঙ্গল। দেশের শারীরিক পরিশ্রম করা শ্রমিক তথা কামলাদের মানুষ সম্মান করে। এই কামলা গুলারে লাথি মেরে চেয়ার থেকে ফেলে দিতে ইচ্ছে করছে। হ্লার পুতেরা বাল ফালাইতে বইছে বিচারকের আসনে। যত অযোগ্য স্টুপিড আর ছাগলগুলারে বিচারকের আসনে বসিয়ে মেজাজ খারাপ করা একটা প্রোগ্রামে পরিনত করেছে।,1,entertainment
বিচারক দেরকে জুতা দিয়ে পিঠানো দরকার সালাদের কথা শোন মন চাইছে কাছে পেলে জুতা পিঠা করতাম,1,entertainment
বালের বিচারক সব গুলোকে পাসায় লাত্তি মারা উচিত যে বালের বিচারক শালা খবিশ,1,entertainment
জাজ গুলা একেকটা মাদারসুদ😠😠,1,entertainment
বিচারক দের গুষ্টি চুদে দিতে হবে,1,entertainment
খানকির বাচ্চা তুই যে ইংরেজীতে কথা বলিস তা টেন্সের সাথে মিলেনা,1,entertainment
বালের কেমেরা ম্যান,1,entertainment
এরা বালের বিচারক,1,entertainment
তোর পুটকি দিয়ে নাগা মরিছ ঢুকাবো মাংস খাবিনা তুই গু খাবি সকালে উঠে এক গ্লাস মুত তুই পান করবি তোর পুটকিটা ফাটাবো তোর খতনা আমি করবো গুয়ের স্যুপ তোকে খাওয়াবো গু খা তুই গু খা।,1,entertainment
দাড়িওয়ালা শালার কাছে টাকা নাই শেভ করার জন্য মাদারচোদ,1,entertainment
সাহারার নাকে দিয়া দুধ গলে,1,entertainment
সানাই একটা পতিতা মেয়ে,1,entertainment
ফাহমি কুত্তার বাচ্চা। ওর দাঁড়ি চাইছা দেওয়া উচিত।,1,entertainment
মাছুদ রানার মারে চুদি আর বিচারক খানকির পুলাদের ভাব হেডা দি বরমু খানকির পুলা মাইয়াদের,1,entertainment
তর বুনেরে চুদি খানকির পুলাচামচার বাচ্চা,1,entertainment
কেউ তাদের দাম দেয়না কারন তারা তাদের ইচ্ছ কিত্র আসেনি তারা সবাই চকরের সিকার তাই কিনতো মালয়সিয়া বা আনসব দেশে বাংলা মহিলারা না মাগিরা আসে তাদের বিসা কে দেয় কয়েকটি মাগিদের যনে প্রবাসিদের কত খারাপ বাসা সুনতেহয় কেন সরকার কি নেই নাকি দেশের নাগরিক মাথা নিচেদিয়ে চলার হিসেবটা সরকার নিযে দিয়েছেন আমি একজন বাঙালি আমি বিচার চাই তানাহলে আমি লাইবে নেমে এটা বলব তখন কেও কিছো যেন না বলে,1,entertainment
পরিচালক কি মাল খাইছে নাকি।,1,entertainment
সালা মনে হয় গাজা খাইছে,1,entertainment
হালার আবাল মার্কা জাজ দের আরো রোস্ট করার দরকার,1,entertainment
খানকি লজ্জা নাই তর মইরা ফুরা,1,entertainment
সানাইকে বলছি কতো জন থেকে চোদা নিছো দুদু তো তোমার ফুটবল,1,entertainment
শালারপুতেরা খালি ট্রেইলার দেস কিন্তু নাটক তো আপ্লোড করছ না বাইঞ্চুদের দল,1,entertainment
কুত্তার বাচ্ছা গুলোর অন্যান্য দেশের গুলোকে দেখে শিক্ষা নেওয়া দরকার। অযোগ্য মূর্খ রা কিভাবে ট্যালেন্ট ছিনবে।,1,entertainment
আমি চুদে ওকে বাচ্চা দেব আমার না ওকে খুব ভালো লাগে আমি ওকে চুদব আর কেউ না 🤱🤱🤱🤱👩‍👦‍👦👩‍👦‍👦💋👄💋👄👅👅,1,entertainment
শখকে আমি চোদে দেখতে চাই হোগাই কত জুর,1,entertainment
সনিতা আসলেই এক্টা ফাটকা মাগি,1,entertainment
মাসুদ রানা হে অাবার কোন হালারে! অার কি কইতাম বিচারকদের বাইনচোদ । তাদের মুখে আমি আর বন্ধু মিলে ছাগলের পেশাব ডালি,1,entertainment
নাম্বার ওয়ান বেশ্যা মাগি মাহি,1,entertainment
"পরিচালক একটা গাধা,,,,<br />এত সুন্দর একটা নাটক এই ভাবে মিল ছাড়াশেষ করে দেওয়ার কোন মানে হয়...!!!!<br />হালারপো হালায় তারছেরা পাগল,,,,<br />আরো কিছু কাহিনি যোগ করে মাতাব্বরের নাতনির সাথে মিল দিয়ে দিলে নাটকটা আরো অনেক সুন্দর হতো,,,,<br />আপনারা কি বলেন....??????",1,entertainment
চুইল্লা হালায় হইতে চাইছে কিন্তু হেয় বেকা হইয়া গেছে ফইন্নি বাঙালী,1,entertainment
এমন বিচারকের দুই গালে জুতা মার তালে তালে শালা বিচারক এরা আসলে নিজেকে কি মনে করে এইরকম মানুষ কি বাবে বিচারক হইছে মানুষ কে অপমান করার অধিকার কে দিয়েছে এদের,1,entertainment
চ্যনেল আই কই পাই মাদার চোদ বিচার গুলা এই খানকির পোলার বাড়ি কই,1,entertainment
বিচারক দের চুদি,1,entertainment
ফাহমি সালা টশা মুরখো সালা,1,entertainment
আমি সানিতাকে চুদবো,1,entertainment
"নাঊযুবিল্লাহ,এক পাগল পরিচালক, আরেক ছাগলে করছে অবিনয়।",1,entertainment
মডেল যতো আছে সব লুচ্চা,1,entertainment
এই মাগির চেহারাই পতিতার মধ্যে পরে ছি ছি ওর চরিত্র খারাপ,1,entertainment
বিচারক নির্বাচন করেছে কোন চুতমারানি।চুতমারানি বিচারক নির্বাচন করেছে।,1,entertainment
বাল ছিড়া নায়ক জাহিদ খান গরুর মতন অভিনয়,1,entertainment
এরে মাদারচোদ ছবির লাস্টের টা কি তোর ভাবির বোদার বিতরে ঢুকাইছোতনি?,1,entertainment
"ওরে হালার পো হালা মানুষ যদি বানর থেকে আসে!!তাহলে হিন্দুরা বলে গরু তাদের মা। তাহলে কি বান্দর এর জরমো কি গরু থেকে?মানুষ যদি পশু থেকে জরমো হইয়ে থাকে তাহলে মা হাওয়া আর বাবা আদম, কই থেকে আস্লো??জুতা দিয়ে পিটাইয়া আধমরা কইরা কেরোসিন দিয়ে জালিয়ে মারা দরকার।। আর সাব্বির আপনার মত একজন অভিনেতা এমন একটা নাটক এ অভিনয় করবেন এটা আশা করি নাই,,,,,",1,entertainment
সানিতা আমার সাতে সুদা সুদি করবা,1,entertainment
দুধ ধরে টিপ মারা উচিৎ 🤣😃😄,1,entertainment
অসম্ভব খানকি,1,entertainment
শালাকে বিচারক নাকা ফকির কিছু তো বুঝলাম না। বাংলাদেশি আবার বিচারকরা তাকে নিয়ে আসে। আমার মনে হয় চ্যানেল । নুনুর নিচে দিয়ে চলে। সালাকে একদম গাঁজাখোরের মত লাগে। কোত্থেকে চ্যানেল আইয়ে গরু ছাগল নিয়ে আসে।,1,entertainment
এটা ভোলে নায়ক ছাগলের ঘরে ছাগল,1,entertainment
এরা বিচারক আগে হাইস্যা লই। পরে কমেন্ট করব😄😄😄😆😆😆। নাহ আজ আর ঘুমাতে পারব না হাসির জন্য😂😂😂😂,1,entertainment
তোমারে চুদি,1,entertainment
এই হালারা কইত্থেকে আসে,1,entertainment
বালের এক্ট্রেস!!! পাহাড়ের মত দুটো দুধ ছাড়া আর কিছুই নেই।,1,entertainment
তুই তুই তুই এতো খারাপ মাগি,1,entertainment
শখ এঁর বুদা বহুত টাইট %,1,entertainment
আবাল গুলা ছাগলামি মার্কা অডিশন নিসে ঠিকি অল্প জলের মাছ বেশি জলে গিয়া লাফাইছে ও কিন্তু কিভাবে না চাইতেও কিছু ভালো মানের প্রতিযোগি কে সিলেক্ট করে ফেলেছে দিস ইজ মাই গভীর প্রশ্ন😕,1,entertainment
তুই তো বোকাচোদা,1,entertainment
শবনম ফারিয়া একটা মাগি পতিতা।আর বিচারক কোন পতিতার ছেলে।,1,entertainment
কুত্তায় চোদেনা যারে জাজ বানাইচে তারে,1,entertainment
প্রভার দূধ গুলি অনেক নাইছ,1,entertainment
নায়িকা ভোদার মতো চেহারা,1,entertainment
এই সালা দাড়িওয়ালা আচুদা আবাল একটা হের নিজের চেহারা আয়নায় দেখছে কখনো বান্দরের মত লাফায় কুত্তার দাম ও পাবেনা এমন আবাল,1,entertainment
দাড়ি ওয়ালা মাদারচোদকে কালা জুতা মার হালার পুত বিচারক হইছো হালা ফকিন্নির পুত,1,entertainment
অর মতো কুত্তা কে হাবিব কখনো বিয়ে করবে না কোনোদিনই না,1,entertainment
"এই শালা খানকির পোলারা , ইসলামের অবমাননা করা কেন হইলো।",1,entertainment
পরিচালক কুত্তার বাইচ্চা আর না হয় এমনnatok kortona...,1,entertainment
এই পাগল ছাগল নাইকা কোথায় যে পায়,1,entertainment
এক মাইগ্গা আরেক মাগির সাক্ষাৎ নেয়।,1,entertainment
তর মার ভোদা কত কইরা তর মায়রে কাপড় খুলে হাটতে বলস কালা বন্দুক তর মায়রে লাগা সালা,1,entertainment
এসব অসভ্য মেয়েদের মা বাবা সমাজে মুখ দেখায় কিভাবে!! ছি । এসব মেয়েকে চড় দিয়ে দাত খুলে দেয়া উচিত । বদমাশ মেয়ে কোথাকার!!,1,entertainment
আমার বাল বিছাক,1,entertainment
সালা বিচারক না গাজাখোর,1,entertainment
সলারগরের সালারা,1,entertainment
এই ভুছকি নাকি রুপের রাজকন্যা।। ইয়াক,1,entertainment
আবাল মার্কা মানে বিচি ছারা বিচারকগুলা কই 🤣🤣🤣,1,entertainment
তোরে কেউ স্বপ্ন দেখুক বা না দেখুক তোর দুধ সবাই দেখে মাগি,1,entertainment
সব লুচ্চা নায়কের দল এক জায়গাই।,1,entertainment
আর তোর সাতে মাগি ছাড়া আর কে আসবে,1,entertainment
নায়িকা কে আসল পতিতা মনে হয়েছে।।।। যেমিন নায়িকা তেমন চরিত্র হিসেবে ঠিক আছে,1,entertainment
আবাল চোদা পরিচালক কিচুই বুজলাম না কুনু কিচুই মিল নেই,1,entertainment
সানিতা তুর সুনাত কছু দেমু মাগি,1,entertainment
ওরেতো পতিতা লয়ের পতিতা বল্লেও ভুল হবে সে তো বিশ্ব বেইশ্যা,1,entertainment
চুদনার পোলারা বালের রেপ চুদাছ আবাল চোদা পোলাপান👎👎👎,1,entertainment
এই শালির অনেক নাটক দেখতাম আর এই বেয়াদব মেয়ের নাটক দেখবোনা শালি শিক্ষত গুরু,1,entertainment
পরিচালোক একটা ছাগোল মসারপ আরেকটা ছাগোল,1,entertainment
বিচারক হইসে ওরেই তো ফকিরের বাচ্চা গো মতো লাগে ওর থেকে আর কি ভালো আশা করা যায় ছাগল দিয়া হাল চাষ করালে যা হয় আর কি।,1,entertainment
মাসুদ রানাটা কোন খানকির পোলা আর এইসব মাগি আর জারজ সন্তানদের বিচারক হিসেবে কে দিল তোরা বিচারক দেওয়ার আগে বিচারকের ইন্টারভিউ নিবিনা তারা কি বিচারের যোগ্য কিনা আরো বলছ বাংলা নাটক আর বাংলা গান শোনার জন্য এই ব্যাইস্যাদের দেখার জন্য,1,entertainment
আমার এ কমেন্ট শাহতাজকে দেখাবেন সবাই দয়াকরে। আমার খুব ইচ্ছে ওকে পাগিয়ে চুদব এবং খুব মজা করে ওর পাছায় বগা ঢুকাব। প্লিজ হেল্প মি,1,entertainment
তোরে চুদি খানকি মাগি।,1,entertainment
তোর ধুদ গোলা হিরো আলম কে দিয়ে টিপা,1,entertainment
হিরু হওয়ার সখ মিটিয়ে দিছে😂 বেশির ভাগ অভার স্মার্ট হিজড়ে টাইপের😃 আমিই হয়তো একমাত্র ব্যক্তি যে মাসুদ রানা কে তাই জানি না😕 এই হোগার পোলারে গার্লফ্রন্ডের সাথে ফোনে কথা বলাতেই দিলো আরেকটারে দিল গালফেন্ডের বিয়ে হয়ে গেছে বলে,1,entertainment
এগুলা দুধ নাকি শীতাকুন্ডের পাহাড়,1,entertainment
এই দারিয়ালা মাদারচোদ কে ওকে তো আমি কোনোদিনোও টিভিতে দেখি নাই,1,entertainment
খানকির আবার লজ্জা সরম😡😡,1,entertainment
মাগিকে কেউ বিয়ে করবে না আমরা ওকে চুদবোও না,1,entertainment
বিচারক গুলো ব্যবহার কুওার চাইতেও খারাপ।,1,entertainment
এইসালা বকা চোদারা এক হিরোর ফটো দেখা ইয়ে বকা চোদা হিরোর ফিলিম চালাশ কেন,1,entertainment
মিথিলা খানকি মাগির পছন্দ টা এতো জঘন্য। শেষ পর্যন্ত ফাহমির মত পাগলের চোদা খাইলো।,1,entertainment
হালার পো হালারা,1,entertainment
বিচারক কে জুতা দেওয়া উচিত শালা,1,entertainment
পুরাই তে ভোরে দিলেন ভাই 🐸🐸🐸,1,entertainment
এমন পোশাক আশাক নিরমাতা লোকদের জুতা দিয়া বাইরান দরকার আমি মাদার চোদদের জুতা দিয়া বাইরাই-------- পোশাকের কোন লছছম নাই।,1,entertainment
তুই মাগি,1,entertainment
আনার জাজ আনার ভাব। ।।।মমর ভাব দেখে হয় ও নাইকা হয়ে আসছে সব।গুলো কুত্তার বাচ্ছা,1,entertainment
খানকির দের মাকে আগে চুদা দরকার,1,entertainment
এই বেসসা মাগির জারক ছলটা কে,1,entertainment
মাদারচুদের দল বিচারক,1,entertainment
তুর মারে তুই চুদ মাগির পোয়া🤬 খানকির পোয়া অন্যকে ছোট করা তুর প্রপেশন এইসব করে টাকা খাস তুর লজ্জা সরম নাই মাগির পোয়া🤬 তুর বদা আছে কিনা হাত দিয়ে দেখ তো মাগির পোলা🤬🤬🤬,1,entertainment
খানকির পুলারা যে বিচারকের আসনে বসছোছ তুরা কয়জন ইন্টারভিউ দিয়া সেলিব্রিটি হইছোছ,1,entertainment
যে বিচারকদের ইচ্ছামতো বাংলা চোদা দিতে পারবো অই ই আসল মাসুদ রানা হিরো ত হিরো ই হয়,1,entertainment
ববি খানকী দুধ দেখাইয়া কয় টাকা পাইছে ?,1,entertainment
খানকিমাগী পারলে তুই আজকে রাতে মাজা তোর মতন মেয়ে বেচে থেকে কোন লাভ নেই তুই নারীজাতির কলঙ্ক ও,1,entertainment
একটা পাগল বিচারক আছে না ছুল গুলা বড় বড় দেখতে দেখা যাই ডাজবিন মানে আর্বজনা এই খানকির পলারে কোন বেশ মাগির পুলা বিচারকের চেয়ারে বসাইছে ওর বউরেও পাটাইয়া দিস তোর গোষ্টির মধ্যে তো সব চালায় রিকশা আর তুই বসছোস বিচারকের চিয়ারে😡😠😡😠,1,entertainment
মাহাস তুই সয়তান হারামি,1,entertainment
এই সোনালী মাথা ওয়ালা বোকাচুদা কে ভাই? মনে হইতেসে গলার ভিতরে ধন ঢুকাই গান গাইতাসে।,1,entertainment
সেই আগের মতনই মাদারচোদ বিচারক জুতা ফিক্কা মারা দরকার,1,entertainment
সব কয়টা জাজ কে কুত্তা দিয়ে চুদানো দরকার। আর এই সালায় আরেক জনের চুল নিয়ে মজা করে আবার জিজ্ঞেস করে সব কয়টা অজ্ঞ ঠিক আছে কি না। এই সালায় নিজেই তো পাগলের মত চুল রাখছে রাস্তার পাগলদের মত আর অর পেন্ট খুললে অর সোনা খুজে পাওয়া যাবে না সালায় তো একটা হিজরা। আর ফারিহা মমো এই মাগি কি বিচারক হয়ার যোগ্যতা রাখে। সব গুলা কুত্তা বিচারক এর জায়গায় বসিয়ে রাখছে। কুত্তা দিয়ে কখনো মানুষ বিবেচনা করা যায় না।,1,entertainment
মাদারচোদ জন্মের ভুলে এমন হয়ছে দাঁড়িওয়ালা । চেহারা দেখে ময়ে হয় গাঁজা খোরশেদ । ওরে আমি পাইলে ভরে দিতাম । চুদির পুলা,1,entertainment
নায়ক না আমাৰ বাল,1,entertainment
সালির বেটি বুঝেনাই নিচ তলা বাড়া দিয়া দুতলা বানানোর কথা টা,1,entertainment
কুকুরের মতো লাগছে ।।।তোর মা আসলে একটা কুকুর।।।রাস্তায় ঘুরে ঘুরে কুকুরের মতো তোরে জন্ম দিছে কুকুর।।।,1,entertainment
এই আবাল বিচারকদের বাংলাদেশে বয়কট করা উচিত।,1,entertainment
এজন্যই বলে আবালচোদা বাঙালী। সৌভিক ১০০% এটার পরিকল্পনা আগে থেকেই জানে।,1,entertainment
মনে আচে কি বিগত দিনের কথা এর মানে কি। খানগির পোলারা বাইচোদ আমি যদি পেথাম মাদার চোদকে জুতা দিয়া পেটাইতাম।।।,1,entertainment
ওই খানকির বাচ্চ খানকি মাগী একটা তোর দুধ তুই পতিতাবৃত্তি করে বড় বানাইছোস সেটা তোর বাপ আর ভাইদের গিয়া দেখা। মাগী খানকি রাস্তায় রাস্তায় দেখাস কেনো। শুয়ার গুলা আবার এই পতিতাকে প্রমোট করতেসে।,1,entertainment
কি রে হালার পুত হা করি থাকচ কা,1,entertainment
ভাই আপনি ঠীক কথা বলছেন এসব গরু ছাগল বাদ দিয়ে ভাল মানুষ গুলোকে বিচারক হিসেবে চ্যায়ারে বসান,1,entertainment
এ কুত্তার বাচ্চা চিমটি করছে রাখছি কি বিচারক প্যানেলে ওদেরকে জুতা বাড়ানোর দরকার মানুষকে অপমান করা হয় জানে জানোয়ারের বাচ্চা ওদেরকে দিয়ে ওদেরকে দিয়ে একটা করানো হোক যতগুলি ছিলে এই জায়গায় আসছে তাদের একটা যোগ্য এই বিচারকরা নয় জানোয়ারের বাচ্চা,1,entertainment
বালের মাসুদ রানা বালের অডিশন বোকাচোদা,1,entertainment
এইরকম আবালচোদা বিচারক দেওয়ার আগে দুই বার ভাবা উচিত ছিল এইরকম বিচারক কেউ তোদে ও না,1,entertainment
হাংকির পুলা মাদার টুস্ট মাদারের বাচ্চা তুই এইটা কি শুনাইলি বাংলা গানরে এইভাবে ডুবাইবি হালা বাইন চুদ,1,entertainment
সানাই সানাই ওরে কুত্তা দিয়ে আর বললাম না,1,entertainment
ও সালির মুখে মালউট করতে মোন চায়বে না আবার বড় বড় কথা বলে,1,entertainment
নাটক দেখতে কারনা ভালো লাগে।মোসারফ করিম তার অবিনয় দারুন।কিনতু। যখন দেখি।তাহার বৌ নাটকের মদ্যে অবিনয় করতাছে।তখনি মনেহয় পাইখানা করে।পাই খানার দিকে চায়া থাকি।,1,entertainment
দাড়ি ওয়ালা শুয়ারটা কে,1,entertainment
তুই নাইকার আওতায় পারছো না তুই খানকির আওতায় আর উপস্থাপিকাকে কি বলবো মেয়ে নামের কলঙ্ক,1,entertainment
শালা ভালো ভিডিও পাঠাত?,1,entertainment
খানকি নাম্বার চাড়া মাগি,1,entertainment
আবাল যতসব,1,entertainment
এই মাগীকে যে বিয়ে করবে তার মনে হয় ধন নাই।। এই মাগির সদর ঘাট তো পুরাই ফাকা।। জাহাজ এমনিতেই পার হবে,1,entertainment
বুদা চুদে,1,entertainment
এতো বড় দুধ দেখে সারারাত কমেন্ট করে করে মাল যে কতো বার ফেলবো,1,entertainment
নাইনচুদের পুলা গোরে বিচারক বানাইছে কে সালির বেটি তরে পাডা দিয়া লাগামু,1,entertainment
চোদা,1,entertainment
আমি মদ খাই আমার মাথা মাতাল ইচ্ছা করতেছে চুদি খানকির পোলা ও মাইয়াদের 🔥🔥🔥🔥🔥🔥🔥🔥🔥🔥🔥🔥🔥🔥🔥🔥🔥,1,entertainment
নিচ তালা ভারা দিয়ে তো দোতালা করছে এবার নিচ তালা আর দোতালা ভারা দিয়ে কি তিন তালা করার সগ জাগছে একটা পুরাই একটা খানকি গাজ ভালো তো ফল ভালো আর কিছু বল্লাম না,1,entertainment
তোমার লাইফ তোমার তোমার দুধ কিন্তুু ফেসবুক তোমার একার না আরেক প্রশ্ন করতে ভুলে গেছেন মাহসান ভাই ওনার এই সার্জারি করা দুধে চাপ দিলে কি বেলুনের মতো ঠাস করে ফুটে যাবে নাকি কিছুই হবে না ইচ্ছা তো করতাছে এক ঘন্টার জন্য বয়ফ্রেন্ড হই আর টিপে ঠাস করে ফাটিয়ে দেই,1,entertainment
এমন চোদানি অনেক আছে।,1,entertainment
নকলে ভরপুরছবি আবাল সুপার সটার,1,entertainment
কুকুরের বাচ্চার ব্যবহার! একদল বলবে আমিওতো খারাপ বলছি,1,entertainment
তোদের চেয়ে মোশাররফ করিম অনেক ভালো শালা আবালরা🤧🤧🤧,1,entertainment
কুত্তার বাচ্চা বাচ্চি রে জুতা দিয়ে পিটানো উচিত,1,entertainment
মাসুদ একটা মাদার চোদ শালা ফকিন্নির পোলা শালার চুলের অবস্থা কি বস্তির পোলা,1,entertainment
হালা একাটা কাইল্লা চোদনার পোলা সৌভিক্কার বাচ্চা,1,entertainment
আবাল খানের আব্লামি দেখতে আসলাম,1,entertainment
এই খানকির পোলা বিচারক দের দেখলে সারাদিন বকা দিতে ইচ্চা করে। মন ভরে না ওদের গালি দিয়ে। কত গুলো পতিতা আসছে বিচার করতে।,1,entertainment
এই মুভিতে ডিসলাইক দিলো কোন কুলাংগার,1,entertainment
এটা কোন বিচারক শালার পুত তুই তোর নিজের চেহারা দেখছো তোর নিজের চ ঠিক নাই তুই আবার বিচারক হইছোস শালা মাদারচোদ,1,entertainment
"মিশা বড় বেয়াদব,,লুচ্চা নাম্বার ওয়ান।",1,entertainment
তোর ইচ্ছে হলে ন্যাংটা হয়ে চলাফেরা কর। মাগী বোরখার অমর্যাদা করিস খানকিমাগী গালি শোনার জন্য অশ্লীল কথাবার্তা বলিস।,1,entertainment
পতিতা ইজ বেটার দ্যান বারোভাতারি 😂<br /><br />এসব বারোভাতারি দের জন্য আমাদের মতন নিষ্পাপ ছেলেরা এভাবেই গোল্লায় যাচ্ছে!,1,entertainment
বোকাচদা গুলা নিজেকে কি ভাবে,1,entertainment
পাগল চোদা কাহিনি ও নায়ক,1,entertainment
দুইটাই মাগি,1,entertainment
"শালারে জুতা পিটা করা দরকার,,একটি নাটকে কোন ভালো কিছু শেখার নেই,,শালারে কিসের জন্য মিডিয়াতে অভিনয় করতে দেয়,,ওর মত অভিনেতার জন্য দিন দিন আমাদের আগের সম্মানটা নষ্ট হয়ে যাচ্ছে,,,",1,entertainment
শালারা তোরা মদ খা,1,entertainment
ভাই হালায় কম দামি নেশা করে আসছিলো।। বিশ্বাস করবেন না ভাই এই অনুষ্ঠান দেখে সত্যি মন খারাপ হয়েছিলো।। কি বলবো আর শুধু ওরে তালি বাজাতে ইচ্ছে করতাছে। খান কি পোলা এটা কনডম দূর্ঘটনায় হয়ছে।।।সরি ভাই অনেক কিছু বলে ফেলছি।।,1,entertainment
কামেরা মান তোই মানুষের চুদাই না,1,entertainment
সানিতাকে অনেক ছোট দেখেছিলাম আর এখন সে এত খারাপ ছবি করে। আর দেহ ব্যাবসা করে,1,entertainment
তাদের বলে লাভ কি যারা সিনেমাতে কাজ করে অথবা যারা আগে কইরা গেছে তারা সবাই চোদা দিয়া আইছে আর যারা আছে তারা চোদা দিতাছে,1,entertainment
মাসুদ রানার মারে আমি চুদি,1,entertainment
বর্তমানে বাংলাদেশ একটা মুসলিম দেশ। আর এই দেশে কোনো অমুসলিম থাকতে পারে আর তাই এই দেশ থেকে বড় দুধ সানাই কে দেশ থেকে বের করে দেওয়া উচিত,1,entertainment
এই সালারে ঝারু পেটার দরকার।,1,entertainment
তর মত ছাগল কোন দিন এমপি হতে পারে না,1,entertainment
আসুদা বিচারক এরা এদেরকে চুদা দেবার প্রয়োজন,1,entertainment
ভোদার বুবলির জন্য আর সাকিবের ছবি দেখতে ইচ্ছে করে না,1,entertainment
দুধ ধরে টিপ মারলে কি সে দুধ ডেলে দিবে,1,entertainment
তুই তর বাপের জন্মের না তর বাপে তরে চুদে মনে হয় তর বাপ মার সরম নাই ফাসি দেয়না কেন,1,entertainment
অই হিজরা মারকা পোয়া কেগু। <br /><br />মাহিয়া মাহি কিতা আমরার সিলেটর মান সম্মান মারিলিত নি। <br />আজাইরা নায়কের লগে ছবি করে।,1,entertainment
তোরা নিজে নিজেরে কি ভাবিস বলতো নিজেদের কোন মার্কেট আছে যে বালের যে নায়েকা সে আবার বিচারক।,1,entertainment
সানিতা তোমাকে আমি একরাতের জন্য চাই তোমাকে আমি ৫০ হাজার টাকা দিব একরাতে তুমি রাজি থাকলে ভল,1,entertainment
হোগা মারা জাজ,1,entertainment
ওরা চোদাই পাইবো মাসুদ রানাকে এতো সুন্দর সুন্দর ছেলেদের কে যে অপমান করলো ওরা মাসুদ রানা পাইবো কই,1,entertainment
দারিওয়ালা মাদারচুদ মনে হয় পাবনা থেকে এসেছে কি যেন নাম তার বালের খার খানকির পুলা,1,entertainment
তুই একটা গরু এর জন্য গরুর হাটে গরুর মাতো মাইর খাইছো,1,entertainment
ফারিয়ার যে ভোদার চেহারা নায়িকা কিভাবে হয় নাকের ফুটা দিয়ে তো টাইটানিক ঢুকতে পারব,1,entertainment
খানকির পোলা দাড়ি ওয়ালারে পেলে জুতা মারতে মারতে হের পুটকি দিয়া দম বাহির করতাম,1,entertainment
বিচারকদের ভাব দেখলে মনে হয় এক একটা কুত্তার চেয়েও অধম,1,entertainment
শালার পুত তোগ খালি জুতা মার,1,entertainment
কোন আবাল এটার পরিচালক এটা কোনো নাটক হলোনাকি পালতু,1,entertainment
কুওারর বাচ্চা জাজদের কাজ দেখ 🖕🖕🖕🖕🖕 যদি দেশে থাকতাম তোদের বিরুদ্ধে মানহানির মামলা করতাম👎👎👎👎 ফকিরনীর পুত 🖕🖕🖕🖕,1,entertainment
আই টিভি বোদার টিভি,1,entertainment
পপি দুধ অনেক বড় কি হলো,1,entertainment
কঠিন মাগি কয় বেডা ছুদে হিতিরে,1,entertainment
জানোয়ার সব বিচারক,1,entertainment
সেক্সি আন্টি অথবা আপুরা থাকলে আমার এই নম্বরে যোগাযোগ করো01726796485 আমি ঢাকা থাকি রাজু তোমাদের ভালো করে সেক্স করবো অনেক মজা পাবে,1,entertainment
মাদারচোদের বাচ্চারা। আর মোমো তো আস্তা খানকি।,1,entertainment
খানকীর পোলা খানকীর মাগী এই ভাবে অডিশন নেওয়া হয়রে মাদারীর,1,entertainment
আবাল জাজ যাত্রাপালা করার যোগ্যতা নাই আইচে জাজ্মেন্ট করতে জুতা মারা দরকার হালাগরে🤬🤬,1,entertainment
দুধ দেখে মাথা নস্ট মেযে জাতির কলক্ক,1,entertainment
বাংগালী রা সব দেখতে কামলা চোদা আবাল,1,entertainment
আমার দারায় গেছে তোর দুধ গুলো দেখে,1,entertainment
বিচারক ওরথাত গরু গুলার মধে এতো পতিভা থাকলে তোরাই মাসু রানার কেরেক টারে ওভিনয় কর সুদু সুদু ছেলে গুলাকে এভাবে ওপোমান করছ কেন,1,entertainment
এই জাতীয় মাগি নারী এবং মাগা উপস্থাপকদের জন্য দেশটা খানকি পট্টিতে পরিণত হচ্ছে।।।,1,entertainment
কি বিশ্রী নায়ক,1,entertainment
রংপুরের মান সন্মান সব শেষ করলি রে মাগী।।😝😝😝😝,1,entertainment
কুত্তার বাচ্চা কয় রংপুর আরে নীলফামারী কইতে কি লজ্জা লাগে,1,entertainment
ওর চেহেরা কুওার পুটকির মতন শালী গাঁজাখোর ওরে দেখতে গাঁজাখোরের মত লাগে,1,entertainment
সাওয়ায় বাল নাই শোষাইয়া মুতে জাজদের অবস্থা ঠিক সেইরকম।,1,entertainment
মান্না স্যার বেঁচে তাকলে।হিজরা শাকিব হিজরা হয়ে তাকতো কখনো নিজেকে সোপারষ্টার দাবী করতে পারতো না।,1,entertainment
"বাস্তবের সাথে মিল আছে,,আসলে এ ধরনের মহিলারা পতিতাদের চেয়ে খারাপ,,পতিতারা তো কোন না কোন সমস্যার কারনে পতিতা হয়,,আর এই সব মহিলারা নিজের ইচ্ছায় চরিত্র খারাপ করে,,এই ধরনের বউ নিয়ে জিবনেও সুখী হওয়া যায় না",1,entertainment
এই খানকিমাগী রে ল্যাংটো ছবি না দিতে বললা বলেন নেকেট ছবি ভিডিও করতে তাহলে মানুষ খাইবো খানকিমাগী রান্না ইন্টারভিউ জেনেও পাগল,1,entertainment
"কোন বলদ চোদা এডিট করছে এটা, এর থেকে আমার ৮ বছরের ভাইগ্না ও ভাল এডিট করতে পারে, মনে হয় মোবাইল দিয়া এডিট করে সিনেমা বানাইছে,হা হা হা এটা একটা সিনেমা, কাহীনিটা ভাল ছিল এডিট আর অভিনয় বাজে",1,entertainment
ভাই ছবিটা আপলোড দিলে কি চুদে নাকি আপনাদের কে,1,entertainment
স্কুল লাইফে একটা ডায়লগ দিতাম তোর যদি এই চোদন হয় তবে হনুমান এর কি চোদন যায়হোক বিচারক দের ভাবের চো নে নিজেকে পুরাই বোকা দা মনে হচ্ছে। আরে ভাই ভাই শবনাম ফারিয়া টারিয়া আর কয়েক নাটকি আছে যাদের নাম বলার প্রয়োজন মনে করছি না। ওনাদের নাটক দেখে এখন কলেজ পড়ুয়া কিছু নির্বোধ ছেলে মেয়ে যাদের নাটকএর একটাই বিষয় যা হল বাবু বেবি মার্কা প্রেম। তারা এমন ভাব চোদায় বাপরে বাপ।,1,entertainment
প্রভা মাগিরে না দিয়ে অন্য নায়িকারে দিলে ভাল হত।আমার মনে হয় পরিচালককে খুশি করেতে দেহ দিয়ে তাই এই প্রভা মাগিরে নাটকে নেয়।,1,entertainment
চোদা খাবে এমন কোন মেয়ে বা মহিলারা আছো শুধু চোদার পাগল মেয়ে বা মহিলারা আমার সাথে যোগাযোগ করো আমি সব ভাবে চুদে মজা দিয়ে থাকি যেমন ফোনে ইমুতে রিয়েলে ও চুদি তোমার ভোদার রস আমি বের করে দিবো তুমি যেমন করে চাইবে ঠিক তেমন করেই চুদবো তোমার সব কিছু ১০০% গোপন থাকবে তোমার কোন খতি করা আমার কাজ না শুধু মজা দিবে মজা নিবে এমন মেয়ে বা মহিলারা এসো মজা করি কল মি ইমু আছে01632067492 imo,1,entertainment
সব কুকুরের ছাওয়ালের মত আচরন করতেছে ।,1,entertainment
ওর দুদু তে ধন ঢুকিয়ে চুদবে,1,entertainment
মমোর দুধ দুইটা ছাড়া অার কিছু নাই।,1,entertainment
ইভানা পাছা আর দুধ গুলা জোশ,1,entertainment
বকচুদ বিচারক,1,entertainment
"মিথিলার ঠোঁট পাতলা,তাই সেক্স বেশি, ওনাকে আফ্রিকার নিগ্রো ছাড়া ঠান্ডা কোরতে পারবে না",1,entertainment
তোদের পাছার মধ্যে টা লাথি দিয়ে দুনিয়া থেকে বিদায় করা উচিত জানোয়ার গুলো,1,entertainment
অই মাগী তর পর্দার সসম্পর্কে কোন ধারনা নাই তুই জাতির সামনে লেংটা হইয়া নাচা নাচি কর কোন সমস্যা নাই তবে ইসলাম ও পর্দা সম্পর্কে কিছু বলিস না কারণ ইসলাম সম্পর্কে তোর কোনো ধারণা নাই,1,entertainment
বিচারক শুয়োরের বাচ্চাকে তো গাঁজাখোরের মত লাগছে,1,entertainment
ছেলে বা মেয়ে উভয় বিচারকদের কে ভরার সময় অবশ্য নিরাপদ কন্ডম ব্যবহার করবেন না হলে এইস হওয়ার সম্ভবনা আছে কারণ উভয় পুটকি মারা পাটি। 😆😆😆,1,entertainment
ভাই কারো কি শবনম ফারিয়ার রেট জানা আছে মানে একরাতের জন্য কত নেয় আরকি। জানা থাকলে জানাবেন প্লিজ। আমি কিছু করব না। আমি একটা বিদেশী কুত্তা পালি তো। তার জন্য। বেচারা ইদানিং খুব সেক্স অনুভব করে।,1,entertainment
ভাই বলার কিছু নাই মিথিলা মাগি কে নিয়ে,1,entertainment
সালা একটা বন মানুষ বেবোহার সিখেনাই ফোকিনির পোলা লুইচা আর একটা মাগির জি,1,entertainment
লুইচ্চা মাইয়া,1,entertainment
বিচারক কুকুরের বাচ্চা,1,entertainment
এখানে বিচারকের আসনে বসিয়ে এক মাগিক ফোনে ব্লু ফিল্ম দেখছে ওই খানকির নাকি আবার আসছে কে হবে মাসুদ রানা তাকে বাঁচায় করতে কোন জগতে আছি রে ভাই,1,entertainment
আমার বালের জাজ 🙄 জাজ হওয়ার কোন যোগ্যতা নেই বুঝতো মজা যদি এমন হতো ওদের সাথে কিভাবে করল!!!! অনেক আশা নিয়ে এসেছিল অনেক ভাইয়েরা এভাবে করে কাউকে না করে সরাসরি ভালো ব্যবহার করলে কি হত!! কিন্তু বালের জাজ গুলু জেবাবে অইখানে তাকলে তাপ্পর না হয় গালি দিয়া আসতাম।।।তাহলে কাউকে আপমার করলে কেম ন লাগে বুজত।।। 🙅🙅,1,entertainment
এই মাগীর নাম কি আপনারা কেঊ কি জানেন পিলিচ বলেন,1,entertainment
দুর খাংকি মাগি একনকার সময়ে কম বয়োসে চুদা দিলে মজা লাগে চুদার জায়গাতে চুদলে ভুদার খতি নাই খারাপ ভিডিও দেছ কেন তকে পুটকি মারি খাংকি,1,entertainment
এইটা একটা চুতিয়া শো এর অডিশন আর তে হয় একটা রোডিস নাকি বাল একটা চুতিয়া শো এর অডিশন। সালা জাজ দের ভাব দেখলে মনে হয় ওরা মানব জাতীর শ্রেষ্ঠ এবং স্বয়ংসম্পূর্ণ ব্যক্তিত্ব,1,entertainment
এই শুয়ারটাহ এমন করে কেন।😪,1,entertainment
চেনেল আই এর পরিচালক গাজা খাইছে না হলে এরকম পগল ছাগলরে বিচারক বানাইছে বালের বিচারক,1,entertainment
ভাই এই কানকির পুলারে বিচারক কে দিছে ওই সালারে কয় জন ছিনে,1,entertainment
তুর মায়েরে তুই পুটকি মারিস সালা দাঁড়ি ওয়ালা গান্জা খুর,1,entertainment
ছাগলের বাচ্চারা নাকি বিচারক।পুরুষ ও মহিলা বিচারক গাঁজাখোর,1,entertainment
এটাতো অভিনয় বাস্তব কিছু খানকির পোলাগো লাইগা মেয়েদেরকে এইরকম হইতে হয় nic,1,entertainment
কত ইস্মার্ট ছেলেরা এমন আবাল চুদা শোতে গিয়ে নিযের সৌন্দর্যকে অপমান করছে,1,entertainment
ফারিয়ার পাছায় লাথি,1,entertainment
ওই শালা শালিরা কবে থেকে বিচারক হয়েছিল,1,entertainment
খানকি মাগীর পুলারা তোদের মা আর বোন দের দিয়ে এসব নাটক করাতি।,1,entertainment
যত পাগল ছাগলে দেশটা ভরে গেছে,1,entertainment
মাদার তোদেরকে কি বিচারক মনে হয়। মনে হয় তোদের পুটকিতে ডিমের থিরাপি দেয়া দরকার নিজেদের চিহারা কখনো আয়নাতে দেখেসিস মাদার চোদ,1,entertainment
সানাইকে কুকুর দিয়ে চোদাও,1,entertainment
দূর পপি শালি পতিতা,1,entertainment
এইটা হচ্ছে বেশ্যা মাগি,1,entertainment
"খানকির পোলায়, পবিএ আরবী হরফ কে বেংগাইছে, জারজ মাদার চুদের বাচ্ছারা",1,entertainment
সানাই তুই তো সালা পতিতা,1,entertainment
তরে আড়ং দুধের কম্পানি খুচছে আমার মনে হয় তর চিন্তা দারা তুই বুলো ফিলিম বানাতে চাস তর জাগা বাংলাদেশে নাই তুই সবাই কে নষ্ট করতে চাস খানকি মাগি,1,entertainment
খানকির পোলারা কি নায়োক 😡😡কি নাইকা 💗💗,1,entertainment
তবুও মাগির ড্রেস চেঞ্জ করবে না। এই বেশ্যা গুলা সবই নষ্ট করলো।,1,entertainment
খনিকের হোলা বিচারকারী তোরে চো দে কোন ডাক্তার এ তোরে জুতা মেরে বাংলাদেশ থেকে বাহির করা উচিৎ তোদের মতো জানোয়ারের জন্য জুতার মালা রেডি পরে যাস,1,entertainment
চুদির পোলারা বাইচুদ এটা বন্ধকরারদরকার,1,entertainment
ববি কোন নায়িকা হল? ওর সোনার মধ্যে নুনু ঢুকিয়ে রাখলেও ওর তেজ কমবেনা। কাদের অভিনয় নেয়!.,1,entertainment
সবকটা জানোয়ার জানোয়ারের মতন ব্যবহার,1,entertainment
হট সেক্সী সুন্দরী মেয়ে চাই চোদাচুদির জন্যা,1,entertainment
এই সপ মাদারের ছবি জে কেডা দেহে,1,entertainment
এই মাগীর পোলা ছবির শুরুতে এড।,1,entertainment
ওরা নিজের কে কি মনে করেন ওরা হে কি এমন হয়ে গেলেন ওরা একটা কে তো ছাগল চুরের মতো লাগে অপমাণ করা শিখেছেন বাট সমমাণ দিতে শিখে নাই,1,entertainment
ভাই মিথিলা একজন পতিতা।পতিতার মুখে সবাই জুতা মারাতে হবে,1,entertainment
চুতমারানীর পোলা বালের ভিডিও বানাও না,1,entertainment
বালের নায়ক,1,entertainment
মাদার চোদ বান্দরে র বাচ্চাটাকে মাছুদ রানা বানাইয়া ফেলুন,1,entertainment
বিচারক দু জনের পুটকি মারা দরকার তাহলে তাদের ব্যবহার ভালোহবে।খানকি আর খানকির োলারা বিচারক।,1,entertainment
মনে হচ্ছে অই জায়গায় আমি থাকলে খানকির পোলাগো মারতাম শিওর🤬🤬,1,entertainment
ভাই রে ভাই! ফাহমি ভাই মোস্তফা কামাল রাজ ভাই এদের নিয়ে কথা বলার আগে তাদের হিস্ট্রি জাইনা তারপর ভিডিও বানানোর পরামর্শ দিলাম। যত্তসব আবালচোদা!,1,entertainment
হাগলের দল,1,entertainment
কুকুরের লেজ ঘি দিয়ে ডলে সোজা করা যায় আধুনিক যুগের খানকি,1,entertainment
বাল টিপনি ফারিয়া খানকি আচুদা মাগি,1,entertainment
তোরে মাগি কুকুরেও চুদবে না,1,entertainment
😂হালা আবাল,1,entertainment
এই মাদার চোদ টকশোর কুওার বাচ্চায় হইল আসল পতিতার সন্তান,1,entertainment
মম কে একটা পতিতার মতো লাগে। অভিনয়ের চেয়ে চোদার জগতে গেলে বেশি নাম কামাবে মাগি। সব কয়টা আবাল বিচারক!!!,1,entertainment
ও ঠিক আছে মাগী আরেকটা মুসলমান ভাতার ধরে নেবে ওর কাজই হচ্ছে এটা,1,entertainment
লুচা খানকী ছেলে তোর মুখে যুতা মারি,1,entertainment
মালাউনদের টার্গেট থাকে ইসলামের বদনাম করা,1,entertainment
তরে কোন সালা গান গায়তে কয়ছে তরে নিয়া বাজারে বিক্রয় করা উচিত,1,entertainment
মাগীর দুধে গজব পরবে ।গরুর দুধের চেয়ে বড়।গরু ফেল খাইছে।মাগিরে বুধা।শুকরের মুখ দিয়ে ওর বুধা চাটাতি হবে।,1,entertainment
কাউয়া কাদেরের সাথ😆😆😆,1,entertainment
শালি তুই একটা বড়ই মাগি,1,entertainment
মাদার চোদগুলা সব পাগল,1,entertainment
এরা কি বিচারক নাকি নটির বাচ্চা দারি টা ওয়ালা পাগলের বাচ্চা,1,entertainment
কে হবে আবাল রানা😂😂😂,1,entertainment
মাগির লজ্জা শরম নাই তার জম্ম ঠিক নাই জারজ সন্তান,1,entertainment
কে এই বাইনচুদ মাসুদ রানা এরে পাইলে আগে জুতাপিটা করতাম,1,entertainment
সবাই লাইন ধরো মাগী কে খাওয়ার জন্য,1,entertainment
নায়ক কেডা😀😀 সালা তেলিসামাত,1,entertainment
মাগিরে আমার কাছে নিয়া আস তার নিচ তালায় কলা গাছ তিমু,1,entertainment
আর শেয়ার তর মার ভোদার বিতর শেয়ার কোরুম তর মায়রে চুদি উওর দে তরমায়রে চুদি,1,entertainment
সব গুলা মাদার চুদ ছিলো বিচারক,1,entertainment
পাগল বলে নায়ক,1,entertainment
সাউয়া রানা। ভিন্ন কায়দায় টাকা ইনকাম চলতাছে,1,entertainment
নেক্সট প্রোগ্রাম কে চু বে ভুটকি শবনম ফারিয়া আর কালা মা গি মম কে🤣🤣 আর ঐ আক্সোদা দুই শালার অন্ডকোষের সাথে পাথর বাইধা দিয়া ভিডিও করতে দেয়া হবে🤐🤐,1,entertainment
কী রে মাঘী দিনে কয় কেজি করে দুধ বিক্রি করিছ।আমি কেজি নিব। তোর দুধের পায়েশ খেতে খুব ইচ্ছা করে।,1,entertainment
ওই হালার পুতেরা তোরা কি বালের জাজ রে,1,entertainment
তারা আমার শাউয়ার ইন্টারভিউ নিছে সব গুলারে চুদি👉👌,1,entertainment
মাগিটারে কেন জে পরিছালাক রা নেয় বুজি না,1,entertainment
এই শালাও সেই দের একটা,1,entertainment
দেশে অনেক পাগল আছে বলেই এইসব রিয়েলিটি শো এর ছাগলেরা এসব পাগলদের নিয়ে মজা করতে পারছে!!!,1,entertainment
"সানিতার চুদা চুদির ভিডিও গেমস দেখতে চাই, পারলে সেটা দেও,",1,entertainment
পাগল চুদা জাজ,1,entertainment
হেডার বিচারক নিজেকে কি মনে করে মাঘির পোলা,1,entertainment
সানাই কে তো দেখতে পারছি না এখানে তো বড়ো মত একটা গাভী দেখা জাচ্চে 😂😂😂😂😂😂😂😂,1,entertainment
দেশের সবচেয়ে আচোদা শো সব জাজ গো মারে চুদি,1,entertainment
কুত্তার বাচ্চাদের লাতিদিয়ে পালাই দেয়ার দরকার চেয়ার থেকে,1,entertainment
ইভানা আপুর পাছা টা জোস,1,entertainment
দয়া করে এই ধরনের ভিডিও আপলোড করবেন না। মুসলিম দেশ। আর কুকুরের বাচ্চাকে পাবনা হসপিটালে দিয়ে দিন,1,entertainment
বিচারকদের মায়েরে বাপ,1,entertainment
আরে শালার ভাই শালা ছবি দেখলে দেখ না দেখলে না দেখ খারাপ কমেনস করিস কেনো,1,entertainment
কোন গাছ বলদে এ নাটক পরিচালনা করছে আবাল,1,entertainment
পুরুষের নাম শুনলে ময়ুরীর মাসিক ছুটে যায়,1,entertainment
মাগি তুই দুদু খাব,1,entertainment
খায় মাগী পোলা তোর বাবার টাকার এম বিউঠায় বিগগাপন দেশ তোর গুটিক চুদু লটির বাটা হোলে বাল নাটক লাব হয়না কত খাইতে চায় তোদের নাটক এই জন্য চলেনা,1,entertainment
সবগুলি খানকির ছেলে বিচারক হয়েছে,1,entertainment
জয় ভাই আপনার রেগুলার একজন ভিউয়ার আমি আপনার বেশ আর কম সব ভিডিও দেখি আমি কিন্তু সব ভিডিও ভালো লাগে আর আজ এমন একটা বেশ্যার আপনি ইন্টারভিউ নিবেন চিন্তা করিনি এমন পতিতাকে হাইলাইটে না এনে এমন পতিতাকে জেলে দেওয়া ভালো আপনি হয়তো সানাই এর পেইজের পোষ্ট গুলা দেখেন নি দেখলে হয়তো ওর ইন্টারভিউ নিতেন না সানাই চাই অপেনলী এর মতো বাংলাদেশে তৈরী করতে এমন বেশ্যার ইন্টারভিউ আর কোন ইউটুবার না নিলে ভালো হয়,1,entertainment
সবাই যে হারে চুদে খাল বানাচ্ছে আমি চিন্তা করছি তোমরা চুদে খাল বানাবা আর আমি সে খালে মাছ চাষ করবো কি বল বন্দুরা আমি কি খারাপ কিছু বলেছি🙄,1,entertainment
কোন মাদারছোদরা যে এসব ভিডিও করে।,1,entertainment
কঠিন হইছে ভাই মাদারচোদের আরো বলার ছিল বাইনচোদ পেত্নীর মতন শালা ঘরের দেখা যায় পাগল মত আবারো হইছে বিচারক বাইনচোদ,1,entertainment
"পরিচালক গরু,",1,entertainment
এরা চারটাই বাস্টার্ড।,1,entertainment
খানকির পুতেগরে চদাইয়া মুরি বিজাইয়া খাওয়ামু মানুসরে অপমান করা ছারা আর কিছু পারসনা,1,entertainment
মাইয়া মানুষ এর আর কোনো কাম পাওয়া যায় না.. খালি বেশ্যা গিরি করে,1,entertainment
বলের ভিডিও,1,entertainment
সানিতারে নাইকা বানাইবো বাল নাইকার বানানোর নাম আর সানিতারে চোদার কাম,1,entertainment
এতো সুন্দর একটা মুভির মাঝে ডিস লাইক দেয় মানুষ এর হলো আসল মাদারচোদ,1,entertainment
আসলে দোষ টা এদের না !! দোষটা হলো কিসু ফালতু ? কনডম কোম্পানির যারা অধিক মুনাফা লাভ করার জন্যে নিন্মমানের প্লাস্টিক ব্যবহার করে যার কারণে কন্ডোমের মাথা অধিক তাপে নরম হইয়া ফুটা হয় যার ফলে পৃথিবীর বুকে আসে এদের মতো কিসু ? আব াল,1,entertainment
ওই সালি জাজ মোবাইল নিয়েই তো সারাদিন পড়ে আছে,1,entertainment
বিচারক দের আচরণ গরু ছাগলের চেয়ে ও খারাপ এসব পশু দের কে জুতা মারা দরকার,1,entertainment
তর নিচতলাটা বারা নিব মাগি সানাই,1,entertainment
একটা খাংকি মাগি আর চ্যানেল গুলা ওরা সব পাগল,1,entertainment
পুলিশ যে কত মাদারী এই ছবিটা দেখলেই বুঝা যায় 🤔🤔🤔,1,entertainment
তুই জে একটা বেশ্বামাগি তা ভালো করে বুঝলাম,1,entertainment
আমার বালের বিচারক হেডার বিচারক থাক আর কিছু বলবো না আমি তো ভদ্র ছেলে,1,entertainment
মেয়েটি একটা মাল,1,entertainment
ওকে কুওা দিয়ে চোদাতে হবে তাহলে ভার্জিনিটি ভাঙবে,1,entertainment
"পরিচালক গাজা খাইলো না আমি গাজাখাইলাম , সত্য ঘটনা না তুলে এইটার শেষ দিলেন কিভাবে , আসল অপরাদি কোথায় গেলো",1,entertainment
এই আবালের বাচ্চা গুলার জুতা দিয়ে পিটা লাগবে নিজের যোগ্যতা নয় অন্যদের কী যোগ্যতার মাপ দেবে,1,entertainment
গরুছুদা সাকিববা,1,entertainment
ও মিথিলা কে নিয়ে ভাবেই না তুই মিথিলার চুদার ভিডিও দেখতে চাষ তাই রাগে এই ভিডিও,1,entertainment
ছিঃ জঘন্য জানোয়ারের মত ব্যবহার।এদের জন্মের ঠিক নাই,1,entertainment
এই বান্দিরপুত কে কে কোন বিচারক হইসে।মাস্তানি লাগাইসে বান্দিরপুলায়।তোর চুল দেখসস।তুই বিচারক হইসোস আবার মাসুদ রানা সিলেক্ট করস।শালা। আর মম তো আমাদের এলাকার গালি দিতে চায়ছিলাম না।নতুন বিচারকের চেয়ারে বসছে যে।যোগ্যতার চেয়ে বেশি সম্মান পাইলে যা হয় আরকি,1,entertainment
সব শালা মাদারচোদের বাচ্চা টা বিচারক মাদারচোদ রে ভুলে গেছে ওরা একসময় নতুন ছিল এপিসোড দেখে মুখ খারাপ না করে পারলাম না সরি গাইস,1,entertainment
মমু কত জনের চোদা খেয়েছে তার কনো খবর বা হিসাব নেই,1,entertainment
সাথে মাগী দুইটাও আছে,1,entertainment
যারা মাসুদ রানা প্রোগ্রাম টি ওপেন করেছে তাদের মাথায় কি কিছু আছে নাকি সালারা ছাগল।দুইদিনের অভিনেতা অভিনেত্রী কে বিচারকের আসনে বসিয়ে দিয়েছে।,1,entertainment
একজন ছাড়া বাকি বিচারকদের হারামজাদা জাদি হারামজাদা জাদি ভাব আছে,1,entertainment
মফিজ রং পুরে মেয়ে রা হয় তার পুরমান মফিজরা সারা জীবন মফিজ থাকবে খানকির দুধ কেটে পুটি মাছ দিয়ে ঝোল করে খাবো,1,entertainment
মিতিলার চাইতে বেশ্যারা অনেক ভালো,1,entertainment
ওই চুল্লা খানকির পোলারে কে বাছাই করার চেয়ারে বসিয়েছে সালা মাদারচোদের বাচ্চা,1,entertainment
সবচেয়ে ভালো লাগছে বিচারক কুত্তার বাচ্চারা,1,entertainment
নায়ক এর জন্য শাবনুরের মানসম্মান শেষ.. এই সব ছাগল পাগল নায়কের কারনে এখন আর মুভি দেখি না...,1,entertainment
এ মাগির দুধ গুলি বেকু দিয়ে পিটতে হবে হাতে দিয়ে হবেনা,1,entertainment
গোপনে চুদা নেলে ফোন কর আমি শাকিল 01844915194,1,entertainment
মমুকে আমরা চুদে দেব্্্্ চুদে বোদা ফাটিয়ে দেব।,1,entertainment
প্রথম দেখলাম বাইনচোদরে কে ও,1,entertainment
শালাদের জুতা দিয়া পেটানো উচিৎ। তারা খুব বড় হয়ে গেছে মনে হয়। বেরল ফারিহার বেটকি মার্কা চেহারা আর অভিনয় দেখলে আমার গা জ্বলে।প্রতিযোগীদের কনবেন্স না করতে পারলে বিচারকের চেয়ারে বসিস কেন রে শালারা।,1,entertainment
শুয়োরের বাচ্চা গুলো এইসব ছবি বানিয়ে আমাদের মুসলমান দের বদনাম করেছে । আমি ভারতীয় পশ্চিমবঙ্গের।,1,entertainment
ওরে পতিতালয়ের মেয়ে রে। তর বাপ কইটা তর মা জে জিজ্ঞেস কর৷,1,entertainment
"তুই একটা মাদারচুদ, খানকির ছেলে, তোকে গালি দিলে গালিকেই অপমান করা হবে নটির পুলা।",1,entertainment
বলদ নায়ক জায়েদ খান।,1,entertainment
মাগি এত খারাপ যে অরে,1,entertainment
সমালোচিত মানে যে জনপ্রিয়তা না এই মুর্খ মাগিরে কে বুঝাবে,1,entertainment
বালের জাজ বালের শো গাঞ্জাখোর জাজ শালা রিকুয়েস্ট আপনারা এসব শো তে না যাইয়া নিজের ক্রিয়েটিভিটি টা সামাজিক যোগাযোগ মাধ্যম ইউটিউবে তুলে ধরেন এসবে যাইয়া অপমান হওয়ার দরকার নাই,1,entertainment
"খানকির পোলারা সৌভিক গংরা নোবেল কে নিয়ে কি ফাতরামি করলো তারপর নোবেল দুই বাংলায় হিট হলো তারপর প্রত্যয় কে চিনে না এখন প্রত্যয়ের পাছায় মুখ ঢুকিয়েছে। সালমান, সৌভিক, আজাদ, তৌহিদ এই বাল গুলোকে মানুষ এখন ঘৃনা করে।",1,entertainment
চেনেল প্রোমট করার জন্য এই পতিতা দের ইন্টারভিউ নিচ্ছে,1,entertainment
বেশ্যা লজ্জা বলতে কিছুইইই নাই,1,entertainment
বোন মানুষ তোকে বলছি তুই জিগাইছোর তোর সাথে দোন আছে কেন মোমোরে আর ফারিয়ারে ওর ধোন দিয়া ছোদাবি সোন তোগো বেটা দুই টারে কেউ চেনে না তোগো বাড়ী কই,1,entertainment
কথা শুনলে মনে হয় তুই ওই মেয়ের চেয়ে বড় পাগল। তুই কি বাংগালী না উগান্ডা থেকে আগতদের মধ্যে একজন পোলাপাইন কথা বলতে পারে না ঠিক মতো আবার মানুষকে পচায়। আবাল,1,entertainment
তুরার মারে চুদ্দাম শুদু বিগ্গাপন,1,entertainment
হায়রে প্রভা মিনিট সেক্স তাও আবার ধন মুখে চুখে,1,entertainment
ফাহমি খাংকির ছেলে তোর বিচির মদ্ধে টা লাথি মারমু। আর শবনম মাগি আর মম মাগি তোদের দুই জনের হোগা দিয়া একটা বাশের বাগান ঢুকামু,1,entertainment
এঢি কি বিচারক না কি ফাজলামি টিবেল ওরা ত সব গুলো মাদারলী,1,entertainment
মহানায়কের ছবিতে ডিসলাইক দেয় খাড়া খাটাশের বাচ্চারা,1,entertainment
মাসুদ রানা কোন সোনার বাল আর এই দাড়ী ওযালা মাদারচোদ টা কে এরে তো এর আগে কখনো দেখিনা এই মাগির পুত নিজে জানে মাসুদ রানা কে মাদারচোদ রে লাগেটা কেমন শালা চোর দুইটা মাগির সাথে দুইটা মাইগ্যা আসছে বাইনচোদ,1,entertainment
মাগী তোরে হোটেলে নিতে চায় মাগী,1,entertainment
এই সব ফালতু মাগিদের কেন আপনি আপনার শো তে বসালেন ভাই ছি ছি ছি আপনাকে দিয়ে এইটা আশা করিনাই,1,entertainment
যশোর মারে চূদি খানকির পো হালার পো হালা,1,entertainment
ছাগল মেয়ে,1,entertainment
মাদারচোদ নাটক না করে। মাগির দালালি করলে ভালো মানাবে,1,entertainment
মাগিরে কুকুর দিয়ে চুদানির কাম,1,entertainment
পাগলের বাচ্চারা এ কি নাটক বানায়,1,entertainment
টাকা পাইয়া মেয়েটা আজ অনেক খারাপ হয়েগেকে লিক ছে দুধ দেখে ধন থাড়াইগে,1,entertainment
জাজ মাল্টিমিডিয়া ভং ধরেছে তারা পিয়ার্স ব্রসনানের লুক আর ড্যানিয়েল ক্রেইগের এটিটিউড ওয়ালা মাসুদ রানা হাজির করবে। সেই হাজির করা মিশনে মাসুদ রানা খোঁজার দায়িত্ব দিয়েছে একাডেমি এওয়ার্ড প্রাপ্ত ডিরেক্টর ক্রাইম থ্রিলার স্পেশালিস্ট ইফতেখার আহমেদ ফাহমি রেকর্ড তেইশবার একাডেমি এওয়ার্ড মনোনীত অভিনেত্রী জাকিয়া বারী মম এবং ডেব্যু মুভিতেই একাডেমি এওয়ার্ড ছিনিয়ে নেয়া শবনম ফারিয়াকে। বাকি দুইজন মহা গুণী বান্দা আছে আমি চিনি না। ক্ষমাপ্রার্থী। অথচ এই মহারথীদেরকে তাদের বিচার কাজ চালানোর আগে হোমওয়ার্ক করার জন্য ইউটিউবে এমিটিভি রোডিসের চ্যানেলে ধরে সাবস্ক্রাইব করিয়ে দিয়েছে। এরকম মাচোদ রানা র অডিশন দেখে আমার স্যানেমা দেখার সাধ মিটে গেসে। ভাই রে হলিউড গ্রেডের সিনেমা বানাবি বলে মাইকিং করতেসস আগে তাদের অডিশন সিস্টেমটা এটলিস্ট শিখ সারা পৃথিবীতে সবাই ছাগল দিয়ে হালচাষ করার সিদ্ধান্ত নিলে মেইসি উইলিয়ামস কখনো আরিয়া স্টার্ক হতো না সুপারব্যাড এ ডেব্যু করা এমা স্টোন একদিন গিয়ে লা লা ল্যান্ড এর জন্য একাডেমি এওয়ার্ড জিতে আসতো না।,1,entertainment
এই বিচারক দের গরুর সাতে বেদে ঘাস দেউয়া উচিত আমার বিচার মতে,1,entertainment
সালার শাকিব পাগলের গোষ্টি শাকিব সালায় হলো পাগল আর ওর ছবি যারা দেখে তারাও পাগল,1,entertainment
এতো দিন মাগিগো অনেক ভালো জানতাম ওরা দি বাইন চোদ খানকি মাগি ভাই ভিডিও টা দেইখা মাথা গরম হয়ে গেছে বন খাডাস গুলা চ্যানেল আই পাইছে কোথায়,1,entertainment
তরে কতজন চোদছে মাগির বাচ্চা,1,entertainment
পরীমনি আবাসিক হোটেলে মাগি,1,entertainment
এই আবাল মার্কা জাজদের দিয়ে হালচাষ করিয়ে বোম্বাই মরিচের ভাম্পার ফলন ফলিয়ে আর সেই মরিচের পেস্ট বানিয়ে তাদের তলায় লাগিয়ে দেওয়া হউক কি কথায় কনো ভেজাল আছে!,1,entertainment
পতিতার আরেক নাম মিথিলা,1,entertainment
কনডম ছিড়ে যে গুলার জন্ম হয় সেই গুলা ই এই রিয়ালিটি সোর বিচারক হয়।,1,entertainment
এই কুত্তার বাচ্চা বিচারকরা ইন্ডিয়ান বিচারকদের দেখে শিখতে পারেনা কিভাবে পার্টিসিপেন্ট এর ব্যবহার করতে হয় এরাই অভিনয় জানেনা আবার আসছে এখানে,1,entertainment
মাংগের বেটি তোক মানুষ স্বপ্নে চোদে মাংগের বেটি নাইকা চোদাইছে। তোর ভোদা ছুতে চায় মানুষ,1,entertainment
সালারা গানজা খাইয়া মুভি বানায়,1,entertainment
"সালার পরিচালক হিন্দু তাই এই বাজে নাটক হয়েছে, তারে জোতা মারা ওচিত",1,entertainment
মাগির দুধ অনেক বড়,1,entertainment
মাগি তুই কোন মায়ের মেয়ে তুর মা কোন পরজায়ের মাগি সালি রেংড়ি,1,entertainment
কুত্তার বাচ্চারা তোগোরে জুতা মারা দরকার,1,entertainment
চ্যানেল আইয়ের মাথা নষ্ট হয়ে গেছে এ ধরনের পাগল ছাগল বিচারক দিয়া মাসুদ রানা খুজতেছে,1,entertainment
মম তোমার জন্য আতা গাছে তোতা পাখি ডালিম গাছে কাউয়া।। সারা শরীর ফর্সা তোমার কালা কেন শাউয়া।। 😆😆😆,1,entertainment
কাজলের ভাই বাবুল রে সাথে নিয়া লইতি হে খুব ভালো এসব পারে। নডি মাগীর পুলারা।,1,entertainment
জাজগুলো দেখলে ইচ্ছে মতো থাপ্রাইতে মুন্চায়😠😠পাদিয়া কেমতে জাজ হয় আই ডোন্ট নো,1,entertainment
সব কুকুর আর শুকুরকে বসাইছে বিচারক সালাদের পেলে জুতা পিটা করতাম ফকিন্নির বাচ্চা,1,entertainment
কি বালের মাসুদ রানা এ কুত্তা দেরকে জুতা পিটা দরকার এ সমাজকে কি শিক্ষা দিচ্ছে অসামাজিক আমি হবো বালের রানা,1,entertainment
মাদার চোদ মুভি কথা কিলার না কেন,1,entertainment
নেকাচুদি তোমার স্বামী তোমাকে চুদবেনাতো অন্যজন চুদবে।,1,entertainment
যারা ডিসলাইক দিছে তারা সব বলদ মাদারচুদ,1,entertainment
মন চায় ওর মুখে পায়খানা করি,1,entertainment
"শখ,অভিনয়জগতে এসেছে শখ করে! এসে নিলয়ের সাথে প্রেম করেছেও শখ করে!সেই শখ করেই নিলয়কে বিয়ে!বিয়ের পরে আবার শখের শখ হল নিলয়কে ছেড়ে দেওয়ার!শখ এ কেমন অদ্ভুত শখ তোমার?যাইহোক তোমার ন্যাকামো কথা আমার খুব ভালো লাগে।অতএব,তুমি ভুল করেও অভিনয় ছেড়ে দেয়ার শখ করে বোসোনা যেন,তাহলে অন্তত আমি তোমার এই ন্যাকামো কন্ঠ শোনা থেকে বঞ্চিত হব।ধন্যবাদ ।",1,entertainment
সানিতা এখন পতিতা হয়েগেছে আমি জানি কারণ পরিছালক ওকে খারাপ খারাপ গালি দিলেও সে কিছু বলে নাকয়েতটা সুটিং দেকলাম,1,entertainment
মাগী সাগী আজ কাল বিচারক,1,entertainment
খানকিপোলা,1,entertainment
তুই তো একটা ফাউল।কুত্তা,1,entertainment
আর তুমি তো শালা বড় আবালের বাচ্ছা আবাল পূটকি মারা তুই গাধার বাচ্ছা,1,entertainment
বোকাচোদারা বিচারক হইছে যত্তসব আবাল বুঝলামনা নাটকের মডেলরা কিভাবে সিনেমার মডেল ঠিক করে,1,entertainment
এই ধরনের বিচারক দের লাথি মেরে বের করা দিয়া উচিত এই ভাবে মানুষকে অপমান করবার মতো সাহস কি করে হয় বোকা চোদা সব বিচারক,1,entertainment
বিচারকদের অবস্থা দেখলে মন চায় পিছে কুত্তা লাগিয়ে দেই হালার নডির পোলাগুলো যাকগে আমি কি কাউকে গালি দিয়েছি ঠেলে দিছি তাই না !,1,entertainment
ওরে বেশ্যা মাগী ইংরেজি বলতে তো পারিস না। আমেরিকান একসেন্ট এ বাংলা বলে কি নিজের রেট বারাবার চেষ্টা করছস তোর মত ছিনাল মাগীদের জন্য বাকি মেয়েরা নষ্ট হচ্ছে।,1,entertainment
পুরো মাগী একটা,1,entertainment
জুতা কি বাংলাদেশে নাই ভাই ৷ শুয়োরের জাতদের পিটা,1,entertainment
এটা নায়িকা নাকি সাউয়ার মাথা,1,entertainment
মাগিরে কে আনচে,1,entertainment
"ইসলাম নিয়া ফান করিস না হারামীর বাচ্চারা..,.,...",1,entertainment
এগুলো তো আবাল মনে হচ্ছে,1,entertainment
"জুই বালের কথা শুনলেই শরীর জ্বলে,বিরক্তিকর",1,entertainment
মানে দাড়াল যে বরিশালের মেয়েরা এই রকম মাগী হয়! নায়লার মত সব মাগীদের বরিশাল থেকে লাথথি মেরে বেরে করে দেয়া দরকার।,1,entertainment
ভার্জিন হতেই পারে এতদিন পথ ভুল করে সবাই গোয়ায় ঠাপাইছে ... সৃজিতের কাছে প্রশ্ন সেও কি পথ ভুল করে গোয়ায় ঠাপালো নাকি আসল পথ চিন্তে পারলো ?,1,entertainment
"মূর্খচুদারা করেছে অভিনয়,",1,entertainment
দুর খানকি মাগী।,1,entertainment
বিচারক যে আড়া চোদা হেতের সাথে মাল ফারিয়া ছিল তাই হেতে নিজেরে অনেক ভাবতাচে তাই সবাইকে অপমান করতাছে।।।।আসলে তার জন্মের ঠিক নাই তাই সবাইকে অপমান করেছে।।।।।আবার সাথে তো একটা মাল আছে ফারিয়া,1,entertainment
নিপু সাকি তো একটা মাগি তার কনো ছবি ভালো কনো অবি নয় নাই,1,entertainment
খানকির পোলা মেয়েদের সরম বলতে কিছু নাই,1,entertainment
জিবনে বহুত চুদন খাইচো,1,entertainment
হোগা মারা সারা গুগল কি বলে !! তোদের যে কে বিচারক বানাইলো রে তার তো ।।,1,entertainment
আল্লাহ কি তোরে দেখেনা। তুই খানকি তো বাংলাদেশের নাগরিক না হাগল ছাগল। বেস্সা । আর জে ভিডিওটা করলে সেও কিন্ত একটা খারাপ ছেলে। নাহয়ে এসব খানকিরে জে কেনো ভিডিও শোতে আনে। দুরো খানকি খানকি খানকি মাগী মগী বাংলাদেশ ত্যগ কর মাগী।,1,entertainment
হুদাই ছেলে গুলার স্বপ্ন ভেঙ্গে দিল শোটি। আর কুত্তার বাচ্চা জাজদের জন্য শত শত ছেলে অপমানিত হল। মানহানীর কেস দিয়ে দিও ভাইয়ারা।। আবারো বলি কুত্তার বাচ্চারা জাজ,1,entertainment
আর ফামিকে সালাাকে পতিতলায় নিয়া দেউ,1,entertainment
বোকাচোদা শালা বিচারক,1,entertainment
এসব আবাল নায়িকাদের চুদাচুদি পরিচালকের ছবিতে অভিনয় করার সুযোগ দিয়েছে চলচ্চিত্র,1,entertainment
মাদারচুদিরে চিনছি বাট মাদারচুদটারে চিনালাম না,1,entertainment
সাউয়ার গান,1,entertainment
বালের মাসুদ রানা বাদ দিয়া রাজ্জাক বা সালমান শাহ তৈরি করুন। যত্ত সব আবালের দল😡😡😡,1,entertainment
শুয়ারের বাচ্চারা! এই জন্যে সবার উচিৎ বাংলাদেশের এইসব ফইন্নি মার্কা শো এর এডিশনে না যাওয়া। থার্ড ক্লাস সব জাজ দিয়ে বালের শো করে। কুত্তার বাচ্চারা।,1,entertainment
দাড়িওয়ালা সালারে আর লাইকা দুইটারে ধইরা বাশি ডেট ফেল গাঞ্জা খাওয়াইয়া থাপরানো জাইতো তবে ভালো হইতো,1,entertainment
মাদার চোদরা মজা করার জন্য বিচারক সাজচত না এত দিন তোদের মতন নিচু মনের মানুষগ নাটক দেখেচে মানুষ চি চি চি সব গুলা গাজা খোর সালর 😡😡😡😡😡😡😡😡,1,entertainment
এতগুলা বাশ দিলেন বাল টা বুঝলোও না নিচতালা মানে কি,1,entertainment
ময়ুরী নাভিটা ভোদার মতোই!,1,entertainment
এই মাগি তোর থেকে হিরো আলোম অনেক অনেক ভালো,1,entertainment
"শালাদের জুতা দিয়ে মারা দরকার,,,👿👿👿",1,entertainment
মিডিয়ার জগত টা মাগি,1,entertainment
ওদের বিচারকদের কে চুদার দরকার । আর যারা অডিশন দিতে গিয়েছে তাদের ও । পাগলদের কাছে যাবে ক্যান বিচারকরা তো আপুর ভক্ত ।,1,entertainment
পভা তোখানকিতার অনেকচূদারভিডীওদেখাযায়তাকেপরিচালককিতাকেনিয়েরাতকাটাই,1,entertainment
শবনম ফারিয়া মম এরা কেমনে বিচারক হয় এদের বাংলাদেশের সিনেমা জগতের অভিজ্ঞতা কতটুকুন ছিঃ লজ্জার বিষয়। আর দাড়িওয়ালা কুত্তার বাচ্চা এইটা।নাম ও জানিনা কুত্তার বাচ্চার।ইতা নাকি বিচারক।যত্তসব আবাল ঢাকায়।চ্যানেলের কাছে অনুরোধ আমার কমেন্ট বিচারকদের কাছে দয়া করে পৌঁছে দিবেন প্লিজ। ফেরদৌস স্যার পূর্ণিমা ম্যাম এরাই বাংলাদেশের লিজেন্ড। বালের রানা চরিত্রের জন্য আবাল বিচারকদের অনুষ্ঠান প্রচারনা করতে গিয়ে আপনাদের চ্যানেলটারও সম্মান রাখলেন না। !,1,entertainment
কুত্তার বাচ্ছা!! এসব বালের অনুষ্টান করার কি দরকার আবাল বিচারক!,1,entertainment
কি বালের জাজ🤔,1,entertainment
আলা হিজরার বাচ্ছারা বাল ছিরো,1,entertainment
ওরা সব জাজ খানকির বাচ্চা,1,entertainment
বিচারকদের ব্যবহার দেখে দেখারেই মন চাচ্ছে না আর দেখবো না বাল রাজ ভাই একদম পারফেক্ট।।,1,entertainment
কচ্ছপ তার মাথা বের করতে পারেনাই....তাই ভার্জিন না বেশ্যা তা দাদাবাবু বুঝতেও পারেনাই...এখানে দুষের কিছু নাইরে পাগলা😂😂😂😂,1,entertainment
যারা প্রকাশে হত‍্যা করেছে তাদের কঠর বিচার চাই। এত খারাপ ভাষায় কোন দিন কারো সম্বন্ধে প্রতিবাদ করিনি। ভাল ভাষায় প্রতিবাদ করলে মনে হয় আমার আত্তা শান্তি পাবেনা। তাই নিজের মনকে শান্তনা দেওয়ার জন‍্য আজ অনেক খারাপ ভাষায় প্রতিবাদ করতে বাধ‍্য হলাম। কেউ পারবেন ওর ফ্রিজের যৌনাঙ্গে মধ‍্যে আগুনে পোরা লাল হয়ে যাওয়া গরম রড দুই ইঞ্ছি ঢুকিয়ে দিতে। এমন ভাবে ঢুকিয়ে দিবেন সে যদি না মরে যায় প্রশ্বাব করতে পারে এবং সারা জিবন সে যদি কোন ছেলের সাথে যৌন‍্য সংগম করতে না পারে। অপারেশনটি হবে ওষুধ খেয়ে বেহুস করে নয় নরমাল ভাবে। তাহলেই ন‍্যায় বিচার হবে। খানকি মাগি ন‍্যায় বিচার চাস আয় তোরে আমি ন‍্যায় বিচার দিমু। ভারত থেকে,1,crime
আমি পর্দাশীল মহিলা দেখেছি কিন্তু অই মহিলার মত পর্দাশীল দেখি নি। আর শালা অরে বকা দিয়া নিজের মুখ না অপবিত্র করুম না।,1,crime
আমার হালার গরের হালা অগল। তরা বন্ড বাহিনির দল।তর শট পিলিমের পুটকি মারি।বাতিজার পুতাইত,1,crime
তুই শালা দালাল,1,crime
হাইরে পতিতা এগুলো সব মাগি পতিতা হাচিনা মাগি সরকার এর কুকুর,1,crime
ডিসির খবর প্রকাশ করেন। লুচ্চা ডিসি কি করছে এখন,1,crime
এই লোকগুলোর জানোয়ারের তো খারাপ,1,crime
মাদারচদ,1,crime
কামরুল রিফাতের মায়েরে আজকে চোদিছি,1,crime
কুত্তার বাচ্চা মহা জামালপুরের মান সম্মান শেষ কইরা দিছস,1,crime
এই মাগিকে পুড়িয়ে মারা দরকার,1,crime
সালার সোনা কাটার দরকার,1,crime
খানকির পোলারে পুটকি মারা উচিত,1,crime
সব মাদার চুদরা দারিয়ে দেকলো,1,crime
সবার আগে মিন্নী কে নেংটা করে কুত্তা দিয়ে চোদানো হওক।থাহলে ই সব সত্যি বেড়িয়ে আসবে।,1,crime
এই ধরনের কুত্তার বাচ্চা শুয়োরের বাচ্চা প্রশাসনের লোকের জন্য বাংলাদেশের সাধারন মানুষ ভালো মানুষ অশান্তিতে আছে,1,crime
সন্তান আছে আবার চুদাস স্যারের দোশ নাই সালীরে ঘোড়া দিয়ে চুদানো দরকার,1,crime
আপনাদের কয়েকটা কমেন্ট দেখলাম মিননী প্রথমে বুঝতে পারেনি কি করছে হাটা তো নরমালি হবে তার জানা নেই বড় কিছু হয়ে যাবে তার ভাবনা ছিল ধরে বুঝি হুমকি ধামকি দিবে।কিন্তূ যখন কিল ঘুষি শুরু করলো মিননী কিন্তূ থেমে থাকেনি চিৎকার চেঁচামেচি করছে কিন্তূ মেয়ে চোদার পাগল সব হালায় ধন গুটিয়ে ভাগছে একজনও সাহসী লোক ছিল না খুনিরা ছাড়া।একটা মেয়ে এনে দেন হালা গো বলবো আমি আগে যাই হালা বাঙালি কুত্তা চোদা জাতী,1,crime
সব আবালগুলো তাকিয়ে তাকিয়ে দেখল।,1,crime
তুরা চুদানির পোয়ার আর কোন কাজ নেই,1,crime
এতদিন কিভাবে চলল মাগীর পোলা,1,crime
এ শালার গুষ্টি তর ফাসি হইতেসে,1,crime
হৈ চৈ করে লাভ নাই আজ যদি নুসরাত আমার বোন হতো তাহলে কুত্তার বাচ্চাদের নিজ হাতে ফাঁসি দিতাম???,1,crime
মিন্নি হল মাগি তারকারণে রিপাত কে মারলো সবাই কে ফাসি ছাই,1,crime
হালারা সব মেয়াদ উত্তির্ন গাজা খাইছে,1,crime
বেহায়া মহিলা পর্দা করে আজ আমাদের সকল হিজাপী নারীদের অপমান করলো।,1,crime
মুন্নি মাগি কে কেন এখোন পুলিশ দরেনা,1,crime
ওর নুনু কেটে দাও,1,crime
শালারেতো দেখাযাই অর্জিনাল একটা মাতাল,1,crime
তোদের ধোনে ইট ঝুলিয়ে রাখা দরকার,1,crime
শালী মিন্নিরে ধর😡😠,1,crime
কুর্তার বাচ্চা অবৈধ বলে আমি কি গালি দিতে পারি মাননীয় স্পিকার।,1,crime
হারে বাংগালি বড় বড় লিকছার দেওয়ার মাজে এক নাম্বার। এত গুলা মানুষের সামনে কোবালো কেউ দরলো না? কেন এত বয়?,1,crime
খানকিদের জন্য অফিস পার্ক গুলো অভায়ারণ্য উঠেছে। আরো কতগুলো ভুদা পার্টি আছে লোকচক্ষুর আড়ালে যেগুলো কখনোই ভাইরাল হয় না।,1,crime
এই কুকুর কে জুতার মালা দিয়ে গুরানো হউক,1,crime
শালা বদমাশ মাগি দালাল পতিতা লেনটা,1,crime
হারামির বাচ্চাদের ফাসি দেয় না দেখেই এরা সমাজে এতো নয় নিচু কাজ করার সুযোগ পায়।। এমন আইন চাই যে শিশু ধরশন করলেই ফাঁসি।। ৷ একটা মা বাবার ছোট শিশু কে ও কোলে নিরাপদ মনে করতে পারে না।। এদেরকে হত্যা করা যায় তাতে পাপ নাই।। আমিন।।,1,crime
ডিসি তো পারেনা শালার স্লো মোশন ওরে কলকাতার হারবাল খাওয়াইতে হবে আর হেতিরে ট্রস ট্রস করে মারতে হবে,1,crime
এই মেয়েটি কে ডাক্তারি চিকিত্সা করা হক ঐ দিন কে ওরা সাথে সেক্স করছে ।,1,crime
মিনি শালী হচ্ছে একটা মাঘী,1,crime
সালাকে চাকরি থেকে বাদ দেওয়া উচিত,1,crime
মিন্নি হলো মে নামের কল্যংক,1,crime
আমিতো একারণে বলে বেশির ভাগ শিক্ষিত মানুষই তো বেয়াদব দুর্নীতিবাজ এবং ঘুষখোর শালারা,1,crime
এদের মতো বদ লুচ্ছারাই পার্কে গিয়ে প্রেমিক প্রেমিকা কে ধরে নিয়ে যায়।,1,crime
এটাকে জেলা প্রশাসক বলা যায় না একটা জানোয়ার ওর শাস্তি হওয়া উচিত,1,crime
গুদের নেশা। একটা ফুটো আর দুটো ল্যাওড়া। মাগীর দোষ।,1,crime
জরিত মানে জরিত সালা কলগার মাগি জরিত দেখলাম তাতে বুঝলাম সব দোষ মিন্নির রিফাত জেতে চেয়ে ছিল কিন্তু মিন্নি যায় নি কলেজ গেটেই দারিয়ে ছিল্ তাকে জোর করাও হয়ছিল ৷,1,crime
এই জানোয়ার অধ্যক্ষ ও অসি সহ সকল অপরাধিকে জন সম্মুখে এনে কঠিন সাজার বেবস্থ্যা করা হউক,1,crime
আর কোন তালবাহানা ভালো লাগে না জানোয়ার গুলোর ফাঁসি চাই ফাঁসি,1,crime
চোদা দিয়া কিসের বিচার চায় বুঝলাম না আর ভিডিও টা এইচডি সাউন্ড থাকলে বেশি মজা পাওয়া যেত,1,crime
ওই হালার পুতেরা আমিন ধর 👊,1,crime
দোষ করেছে পরিবারের মানুষকে জানোয়ার বানিয়ে এখন কান্না চোদাও,1,crime
যে সব শালারা জড়িতো সবাই রে ফাসি দিয়ে মেরে ফেলাহক মিন্নি ও অাসলে মাগি জড়িত,1,crime
সালার বিছা কাটি দেয়,1,crime
কি বালের নিউজ করছে এসব দেশটা কে রোহিঙ্গা ধ্বংস করে দিচ্ছে এটা নিয়ে কিছু করেন।,1,crime
এতগুলা মানুষ দাড়ানো কেউ এগিয়ে এলোনা নোংরা মিন্নি বারে বারে নয়নকে না ধরে রিফাতকে ধরলে সে হয়ত বেচে যেত,1,crime
কুত্তায় চোদে রাস্তা ঘাটে হাসে চোদে বিলে! জামালপুরের ডিসি চোদতে গিয়ে গিট্টু লাগাইছে বালে। ! 🤣,1,crime
সন্তানকে মানুস না বানিয়ে জানোয়ার বানাইছ এখন ভোগান্তি কাওকে কাদালে কাদতে হয়,1,crime
স্যারের দোষ দিবি কেমনে তুই তোর মতো তেঁতুল দেখলে কার জিবেই না জল আসবে তাছাড়া তোর যা বডি স্ট্রাকচার জব্বার জিনিস নিগ্রো দিয়ে তোরে খেলানো যাবে এক সাথে টা লইতে পারবি তুই না জানিস স্যারের সংসার আছে তুই কেনো দুধ খাওইয়া স্যারকে মাতাল বানিয়ে উল্টা স্যারকে রেপ করলি ভিডিওতে যা দেখলাম স্যার তোরে কিছুই করতে পারে নাই তুই উল্টা স্যারের উপর চড়ে চড়ে উঠতে ছিলি যাইহোক কারো সংসারে অশান্তি করার আগে বিবেক খাটানো উচিত আর তোর মতো মহিলা কারো মা হতে পারে না সত্যি কারের গর্ভধারিণী মা কখনো এমন কাজ করে না অভাবে পরলে মানুষের বাসায় কাজ করে খায় নোংরামি করেনা বেশ্যাবৃত্তি করেনা।,1,crime
বদমাইশ বানচুদ,1,crime
ইগু একটা মাগি এর বিচার চাই,1,crime
মাগিরে আর মাগির পুলারে এই দুইটারেই ডিম থ্যারাপি দেওয়া হোক।,1,crime
ভিডিও দেখে তো স্পষ্ট বুঝায় যাচ্ছে যে এটা সত্য তো এতে আবার তদন্ত সুদানোর কি আছে বাইন্চোতের ভাব দেখেই বুঝা যায় যে কাজটা শালার বেটা আসলেই করছে।,1,crime
কুত্তার বাচ্চাকে ফাঁসি দে 😡,1,crime
মাগি তুই বেশ্যা তুই খানকি তুই এখন গলায় ফাস দিয়ে মারা যা দেশের মানুষ তাতে সস্তি পাক,1,crime
মাদার চোদ মিন্নিরে তুই বিয়া করবি তাই মননির সাফট করছ।,1,crime
বালের তদন্ত করবে,1,crime
মাদার চুত তুই চোর তুই মিথ্যা বাদি,1,crime
সালা বাটপার চেহারা দেকলেই বুজা জায় তুই একটা লুইচচা বদ মাইছ,1,crime
সালা গান্জা খুর এই সব পাগলের মেলা,1,crime
নটি নাম্বার মাগী ও চিটিংবাজ।,1,crime
এই মাদারচোদ জনগণের কি সেবা করবো,1,crime
জুতা মার মাগির চাওয়ালরে,1,crime
হালারপো মিথ্যা হেডিং দেস কেন,1,crime
এই কুলা লংগার বাচ্চাকে উপযুক্ত সাজা দেওয়া হোক,1,crime
সালা তুই একটা কুকুর তোকে কুকুরের সাথে তুলনা করলাম এত সুন্দরী বৌ তার পর ও ময়লায় চাটা দেও কি করে,1,crime
শালার পুত নিজে আকাম করে নিজেই তদন্ত করবে। হাইরে বাংলাদেশ,1,crime
চুদির পুতেরে বানানো হোক,1,crime
ওই মাগির এতে হাত আছে নিশ্চিত,1,crime
মাগি মজা পাইছিষ তুই ডিসির মাল ভের করে সাথে আরও অনেক জনার তুর ভিডিও দেখে মাল আউট হবে অনেকের আর দোষ করে বিঁচার চাইছিষ তুই তোর ভোদার ভিতর এসিড দিয়ে জ্বালাইয়া দেওয়া দরকার খাংকি মাগি মানুষ দেখলে দোষ তুই যা করসিছ কা কিছুনা,1,crime
ভাব চুদাইয়া কান্না করো মানুষেরে দেখাও একজন জীবন্ত মানুষকে পুড়িয়ে মারছো তার কষ্ট কতটুকু হয়েছে জালিমের বাচ্চারা তোরা খুনি তোদের জন্মের ঠিক নাই,1,crime
মাগি সারের দোষতো অাছে সাথে সাথে তরও চাকরি যাবে স্বামীকে রেখে অনন্য পুরুষের সাথে পরোকিয়া কর সালি খানকি মাগি তুই হলই দ্বিতীয় মিন্নি,1,crime
শালা তর মাকে ছুদি,1,crime
এই লুইচ্ছার ফাঁসি চাই,1,crime
দরাখাওয়ার পরে এখন সব বাইন্চদে বলে এমনই আসছি,1,crime
সালা আবার মুখ দেখায় কেমনে।,1,crime
কানকির পোলাকেগো সবার সামনে ফাসি দেওয়ার দরকার। কিভাবে মেয়েটাকে আগুন দিয়া পুড়াইয়া মারছে। ঠন্ডা মাথায় কিভাবে এই কাজটা করতে পারে।,1,crime
লুচ্চা প্রশাসন,1,crime
শালা তুই পড়তেই তো পারিস না!,1,crime
মিন্নি নামের পুরুষ বিলাসী এই বেশ্যারে থার্ড ডিগ্রি দিলে সব তথ্য আয়নার মতো পরিষ্কার হয়ে যাবে।।।।ঐ বেটির মাল্টিপ্লাগ মার্কা পরকিয়া আর যৌনতার বলি হলো এই রিফাত,1,crime
সালার দুশ্চরিত্র,1,crime
অজ্ঞান হাওয়া এগুলো সব নাটক এই খানকি মাগীরে রাস্তায় ফালাইয়া সাধারন জনগন মিলে চোদা উচিত,1,crime
বগা ফুরি ডি সি সাথে ছুদা দেয়।।,1,crime
তোর মতন বেশ্যা নড়ির কারনে আজ সমাজ টা নষ্টু হয়ে গেছে তুই রেনডি কি করে বললি ছারে র কন দোস নাই তাহলে দোস তোর বোদার,1,crime
নিশ্চয়ই এখানে বিএনপি জামাতের বড় হাত আছে তাড়াতাড়ি খতিয়ে দেখা দরকার প্রশাসক কার্যালয়ে আকাম কুকাম দেশ কত উন্নত হয়েছে আর কত কি দেখাবি সাংবাদিক মিডিয়া আস্তা খানকিরপুত তাদের কারণে আজ এই দশা দেশের আকাম কুকাম তদন্ত করবে শিয়ালের কাছে মুরগী,1,crime
ওকে টাকা রোজের টা কামলারে দুই বেলা খাওয়াইয়া পরে চোদানের কাম চোদমারানির মাগি।,1,crime
এক কাজ কইরেন পুরো ভিডিওটা চ্যানেলে দিয়ে দেন। ঘোলা করার দরকার নাই। সালার নিওজ চ্যানেলেও সরাসরি ভিডিো দিয়া দেয়।,1,crime
ভিডিও ফুটেজ থাকার পরও এই কুত্তাটা এভাবে বাইরে বিচরণ করছে।।,1,crime
বালের তদন্ত কমিটি গঠন করবো বাইন্চোদ এর দল চোখে দেখা ঘটনা আবার তদন্ত করবে,1,crime
জুতা মার হালারে,1,crime
মাগি বুরখা খুল,1,crime
মিন্নি মাগিটার নম্বর আসামি হওয়া উচিত,1,crime
কুলাঙ্গার কুত্তার বাচ্চা কাজ করার আগে কি কিছু বুঝছিলে,1,crime
আই সব মাগি গো পতিতালয় রাখা উচিত,1,crime
লুচ্চা শালা,1,crime
এই শালি আসল খুনি সিসিটিভিতে পরিস্কার দেখা যাচ্ছে রিফাত কে জখন কিল গুসি মার ছিলো তখন এই মিন্নী সাবাবিক ভাবে হাটছিলো এই আসল খুনি,1,crime
মজা কর শালি,1,crime
খানকির পোলা একটা জারজ সন্তান কুত্তার বাচ্চা মিডিয়ার সামনে মুখ দেখায় কিভাবে খানকির পোলায় কুত্তার বাচ্চার তো গলায় দড়ি দিয়ে মরা উচিত,1,crime
হুম ধরা খাইলে সব পেক হয়ে জায়।মাদার সোদকে। আর ঐমাগিকে জুতার মালা গলায় দিয়ে সারা বাংলা দেশ কে দেখানো হক,1,crime
এই বেশ্যাদের আগুনে পুড়িয়ে মারা উচিত,1,crime
তর বাড়ি কইবে শালার বাচ্ছা আচুদার গরের আচুদার বাচ্ছাইন মিন্নি তর মা লাগে নাকি যে মিন্নির দোষ তুলে ধরলিনা।,1,crime
জানোয়ারকে জুতা পিঠা দিয়ে বাহির করা হোক,1,crime
বরগুনার সব পুরুষ দিয়ে বৌ মাগিকে চুদানো হোক তাও মোনে হয় বৌ মাগির জালা মিটবে না,1,crime
এক মাদারচুদে কয় লাখ টাকা হারছে ওরে বলে একজনে ভালো ভালো খাবারে কথা বলে নিয়া আসছে😂😂,1,crime
ভন্ডটা শুধু মাগিবাজ নয় মনেহয় নেশাখোর ও কেননা সালা কেমন করে হেলেদুলে কথা বলছে।।,1,crime
এখানে খতিয়ে দেখার কি আছে শালা লুচ্চা,1,crime
কোন বালের বিচার চাও। মজা তুমিও পাইছো স্যারেও পাইছে 😂🤣😂,1,crime
বাহ ভাই। পর্নো চ্যানেল খুলে বসছেন দেখি 😂😂😂,1,crime
প্রমোশন ভাই প্রমোশনের আসায় চোদা খাচ্ছে মানবতা আজ ময়নার মার ভোদার চিপার গন্ধে মারা যাচ্ছে,1,crime
ভাল করে চু দাচুদি কর,1,crime
উচিত শিক্ষা হবে খুনীদের কাউকে পুড়িয়ে মারা পিটিয়ে মারা কেটে মারা ধর্ষন করে মারার আগে জানোয়ার গুলো চিন্তা করবে এবার থেকে। প্রত্যেকদিন খুনের খবর কোথাও না কোথাও বাংলাদেশে। খুনের যেখানে শাস্তি থাকবে একমাত্র সেখানেই খুন বন্ধ হবে।,1,crime
তুই নটীর বাচ্চা ফাঁসি দিয়া মোর তুই মরে জামালপুরের মাটিকে কলঙ্কমুক্ত কর তুই তাড়াতাড়ি ফাঁসি দিয়া মোর নটীর বাচ্চা নটি,1,crime
মাগি কে পাবলিক কেনো দোলাই দিচ্ছে না,1,crime
এই শয়তানের বাচচারে ফাশি দেওয়া দরকার,1,crime
লুচ্চা বদমাইশ চোর বাটপারদের বড় বড় পদে বসিয়ে দিয়েছে আরো অজানা কতকিছু যে আছে আর কালে কালে আরো কত কি যে দেখতে হয় কে জানে!,1,crime
সব লুচ্চা,1,crime
মাগি তার মানে জামাই একটা কাইচিস,1,crime
সালা দেশের কিযে হলো টাকার জন্য বুরার চোদা খায়। আর আমরা সালা দন কচলাই মরি।,1,crime
স্যার এর কোন দোষ নেই তার মানে তুই নিজ ইচ্ছায় স্যার এর চোদা খাওয়ার জন্য গেছিলি। কেন তোর স্বামী তোকে ভালো করে চুইদ্দা তোর ভোদা ঠান্ডা করতে পারে না। চোদা খাওয়া বেশহা মাগি। এভাবে গোপনে আর কতবার চোদাচৌদি করচিলি। জাতিও বেশহা মাগি। আবার হিজাব পরছে ।,1,crime
সালার ধনেও জর নাই। ঠিক ভাবে চুদতেও পারে না।,1,crime
খতিয়ে দেখার কি আছে আগে তার নুনুতে ইট বেদে দেওয়া হউক জাতে আর কোন মাদার চোদ এই সাহস না পায় কি বলেন আপনারা,1,crime
এই খানকির ছেলের সোনা কাইটা ফালায় দেখ,1,crime
সালা লুচু মিয়া,1,crime
শুয়েরের বাচ্চা কিশের জেলা প্রশাসক,1,crime
আপনি প্রমাণ করার কে আপনার এত চুলকানি কা ফাইজলামি চুদান,1,crime
মিনিট কে করছে জানস না ভাব ভুদাছ !!,1,crime
মোরাজদি একটু এখানে সেখানে চুদি হেতেও দোশ হয় 👙এহোন জে কাজের বুয়ারে চোদে তাতে কোনোদোস।নাই,1,crime
রিফাত মরার আগে দিন রাতের বেলা নয়নের সাথে ছিল ওই খানকিমাগী সেখান থেকে পরিকল্পনা করে খানকিমাগী ওর মা একটা খাঙ্কি ছিল এজন্য ওর মেয়ে এইরকম হইছে,1,crime
ডিসি একটা পাটা,1,crime
হ্যা তদন্ত কইরা বাল ফালাইয়া খালে নামাইয়া দিবা!! সেটা সবাই জানে,1,crime
খোলামেলা পোশাক পরে এতদিন জুয়ার আসর মাতিয়ে রেখেছে আর আজ ক্যমেরার সামনে লজ্জা লাগে। ওর পাছায় লাথি মেরে তোলেন। দেখলেই কেমন বেশ্যা বেশ্যা লাগে।,1,crime
এই মাগির ফুলার বোইরে ছুধার ধরকার,1,crime
হের সোনা কেটে জুলাইয়া রাখবার উচিত লুচ্চা সালায় বলে ডিসি।,1,crime
যারা ওকে ধরে নিয়ে গেছে তাদেরকেও জবাই করা হোক ওখানকার মানুষগুলো কতবর জানুয়ারের বাচ্চা ফিরাইতেও গেলেো না,1,crime
মিন্নির পাচা দিয়ে গরম ডিম দিলে সব বের হয়েজাবে এই শালির সব কিছুই মিথ্য আর তুই কি ওকে বিয়ে করবি নাকি সালা,1,crime
এই কুক্তার বাচ্চাদের ফাঁশি চাই অতি তারাতারি,1,crime
চোদানীর মাগী ভালমতো চুদা খেয়ে খুশি হয়ে বলতেছে স্যারের কোন দোষ নাই। খানকিরে শাহবাগ মোড়ে এনে নেশাখোরদের দিয়ে প্রকাশ্যে চুদানো উচিৎ।,1,crime
শালাকে জামাই আদর করেন,1,crime
হায়রে মাগী!,1,crime
ফাসি হোক মাগির পোলাগো,1,crime
খানকি মাগি তোর ভো আগে ফাটানো দরকার ।,1,crime
চুদির পোর প্রকাশ্যে পাসি দে,1,crime
তাহলে মাগি কার বিচার চাইস!!! করছ ভুল শিকার করলে তো বাচঁতে পারতি!!!,1,crime
কতোটা নিলর্জ্জ শুয়োরের বাচ্ছা আবার কেমরার সামনে কথা বলে,1,crime
শালার পুতের ভিডিও থাকিও নাকি তদন্ত করতে হবে তার জন্য। আর বিরোধীদল এডিটিং করা কোন ছবি ফেলে সেটা দিয়ে গ্রেপ্তার করে ফেলে। দেশটার একেবারে শেষ করে দিল শুয়োরের বাচ্চারা। এর জন্য শতাংশ সাংবাদিকেরা দায়ী।,1,crime
এই মাগীর বিচার চাই খানকি ইবলিশ,1,crime
ওনাকে ভালো করে পালিশ ম্যান দিলে সব বেরিয়ে যাবে লুচ্চা একটা,1,crime
নয়ন মারে চুদি ও কেমোন মাস্তান দেখতাম জোদি দেশে থাকতা মাঝে মাঝে ভাবি জোগদি এ সোব মাস্তান দের চুদার জনো,1,crime
এসব মহিলা নামে কলঙ্ক।।। নিজের অপরাধ ধরা পরছে দেইখা এখন কত কিছুই বলবে।।।শালি বেস্যা মাঘি,1,crime
এই মাংগের বেটি নেশা করে তা দেখেই বুঝা যায় এই শালিও জড়িত,1,crime
ওর মুখে জুতা মারেক জানোয়ারের বাচ্চাকে জারোজ কুত্তার বাচ্ছা শুয়ারের বাচ্চা,1,crime
বাংলায় একটা কথা আছে হরলি দোষ নাই কলি দোষ হয় তুমি চুদা দাও তাতে দোষ নাই আর যে ভিডিও করেছে তার দোষ হয়ে গেল,1,crime
লাশ দেখতে চাই সালা দের,1,crime
লজ্জা হয় নিজেকে বাংলাদেশি ভাবতে একটা ছেলেকে নির্মমভাবে কুপিয়ে জখম করছে আর সব হিজড়ার দল দাঁড়িয়ে দাঁড়িয়ে তামাশা দেখতাছে,1,crime
কেন এ সম্পর্কে সংবাদ পচার করবেননা লুচ্চা ডিসিযে বললো এধরনের ডিসি মানুষের কি সেবা দিবে এসালারাত আছে সোনার জালা নিয়ে বাসতো মাদারচোদ লুচ্চা ওর মা জানে ওর আসল বাবা কে,1,crime
লুইচ্চা বেডা তুই,1,crime
ওর বিচি কেটে দিন। সালা গান্জাখুর। দেখতেই দেখা যাচ্ছে মাতালের মতো।,1,crime
সাংবাদিক ভাইয়েরা আপনারা মনে করেছেন বাংলার জনগন ভোদাই আসলে তা না যেখানে মুক্তিযুদ্ধে কেলাব তার সাথে আমি লীগের পার্টি অফিস সেখানে পুলিশ সব ধরনের আইন শৃঙ্খলা বাহিনীর লোকজন থাকেন এতদিন তারা কি করেছেন আর সব দেশে জুয়া খেলা চলে আর কেলাবে সমস্যা নাই,1,crime
এইসালারে চাকরিচিতকরাহ্যক,1,crime
দুই মাগির মেয়ে দুই মাগি একটি নতুন আর একটি পুরন তোদের ভাই বোন নেই মাগিরা?,1,crime
ধোনের কথা বলে,1,crime
সালা বদমাইশ,1,crime
আস্তে আস্তে আওয়ামীলীগ কুকুরদের সব কুকমো ফাঁস হবে সামনে,1,crime
এসব খানকির পোলারা আবার আইনের লোক ওদের মায়রে চুদি,1,crime
বরগুনাতে মানুষ থাকেনা থাকে সব জানোয়ার এর দল আর ছেলেরা সব হিজরা,1,crime
এক বেশ্যার দেশে বসাবাস করতেছি আমরা।,1,crime
বাল,1,crime
আধা ঘন্টা ধরে ডলাডলি আর হাত মারার পরও ধন দাড় করাইতে পারে না যে ভাদাইম্যা সে আবার কি বালের লীলা করলো হা হা হা,1,crime
হারাম যাদা তুই কি করে করছত মেয়ের কিছু হয়নি হালার পোয়া,1,crime
ডিসি এবং ঐ মাগি দুজনেই খানকির পোলা।,1,crime
সালার যত সম্পত্তি আছে সব বাজে আপ্ত করা হোক,1,crime
খাংকির পোলা তাও আবার সিকার করেনা,1,crime
কুলাঙ্গার সন্তান জন্ম দিলি কেন তোরা।,1,crime
সালার পুতের চেহারা এবং কথাবার্তা প্রমাণ করে সে লুচ্চামি করচে,1,crime
এই বদমাইশতোহ্ ডি সি লীগ🤦‍♂️🤦‍♂️,1,crime
তুই কাদস কেন সালা বলে কি জানে না কেন ফাসি দেই,1,crime
বোকা চোদা তুই,1,crime
কাউয়া কাদের বলবে ওরা চুদাচুদি করেনি শুধু কুলাকুলি করেছে,1,crime
তুইতো একটা কুত্তার বাচ্চা। তুইও নুসরাতের খুনের সাথে জড়িত ছিলি মনে হয় মাদারচোদ। নুসরাতের জলন্ত দেহ দেখে তোর চোখে পানি আসিনি।খানকির পোলা ভিডিও বানাস কাদের নিয়ে।মাদারচোদ,1,crime
চুতমারানির পুলা কানকির পুত তুরাইতো দেশের ব্র বিশ,1,crime
জানোয়ার গুলোর ফাসি হক আমিন,1,crime
চুপ থাক খান্কি চুদাচূদি করার সময় মনে ছিল না ওই এতিম ছেলের কথা,1,crime
কুত্তা দিয়া চোদাও খানকির পোলারে,1,crime
মিন্নির ব্যাবারে নয়ন এর কনো দোষ ছিলো না মিন্নী একটা খাংকি মাগি,1,crime
ওকে তো আগে পতিতালয়ে দেখা গেছে ওই রকমি বডির গঠন,1,crime
নাইকা তো মাগির ব্যবসা করে তার রেইট কতো??,1,crime
সালা কুকুর,1,crime
মাদারচুদ মিত্তা খতা বলচে মাদারবোর্ড মাদারটেক মাদারচুদ,1,crime
পাছার উপরে লাথি মারের কুকুরকে,1,crime
এই মিননি খানকিরে জবাই করা হোক আরে শামিরে বাচাইতে হোইলে শামিরে জরাইয়া ধোরতি দুই একটা কোপ খাইতি তাহোলে বুঝতাম যে তুই সামিরে বাচাইতে চেষ্টা করছোত আসোলে খানকি তুই তর সামিরে খুন করাইছোত,1,crime
এরকম মাগীর পোলাদের জন্যই ধর্ষকেরা ছাড় পায়।,1,crime
বাটপার সালা,1,crime
মিন্নি মাগি পাসি চায়,1,crime
লম্পট ডিসি,1,crime
লোকটা তো খুব ভদ্র জানোয়ার।,1,crime
তুই মাগি একটা খানকি তুই হলি নাটের গুরু,1,crime
ওর মারে চোদ,1,crime
খানকি মাগি কয় কি স্যারের কোন দোস নাই।,1,crime
এমন ভাবে ছেলেটাকে মারলো আর এই সব জানোয়ার গুলো তাকিয়ে দেখলো? হায়রে সোনার বাংলাদেশের মানুষ। দুই জন মানুষ যদি এগিয়ে আসতো তাহলে এই ভাইকে জীবন দিতে হতো না।,1,crime
অপরাধ অপরাধী কোনটার সমালোচনা করবোনা শুধু একটা জিনিসই দেখতে পেলাম এখানে এত লোকের ভিড়ে একটা লোককে এভাবে নির্মম ভাবে কুপিয়ে মারল একটা মানুষ এগিয়ে গেল না তাই এমন জাতির উপর ধিক্কার ছাড়া আর কোন কিছু বলার থাকে না। বাংলাদেশ একটা ভীতু জাতি,1,crime
মাদারচোদ দুর্নীতিবাজ ঘুষখোর হারামখোর লুচ্চা বদমাশ ধর্ষকের বাচ্চা ধর্ষক এখনো গলায় দড়ি মরলোনা,1,crime
যুদ্ধকালীন সময় আওয়ামী গোষ্ঠী ভারতে পালিয়ে গিয়ে দাদা বাবুদের সাথে আকাম কুকাম করে জারজ সন্তান জন্ম নিয়েছে আর স্বাধীনতা শেষে সেই ‌জারজ রা দেশে এসে মুক্তি যোদ্ধা সেজে শহীদ মুক্তি যোদ্ধাদের অবমাননা করে মুক্তি যোদ্ধা ক্লাব নাম ব্যবহার করে সেই ক্লাবে নারী পুরুষের অনৈতিক কাজের কারখানা গড়ে তুলেছে। এ হলো খুনি হাসিনা আওয়ামী গোষ্ঠীর নীতিমালা ও রাজনৈতিক কাজ ॥,1,crime
গুদের ব্যাবসা করে মেয়ে গুলা,1,crime
মিণ্মি একটা মাগী,1,crime
পতিতা মিন্নির ফাঁসি চাই!!🤔 তুই ভালো না মেয়ে গানটা রিফাতের জিবনের সাথে পুরপুরি মিলে গেলো! একটা বিশ্বাসঘাতক বেইমান লুইচ্চা লাফাঙ্গা মেয়ের কারণে অাজ জীবন্ত দুইটা যুবক মায়ের বুক খালি করে লাশ হতে হলো!!!😓😥😭😭😭,1,crime
এখানে মিন্নি নাটক করে রিফাতকে বাড়ী থেকে নিয়ে এসে ওর ভাতারকে দিয়ে মারিয়েছে ও একটা খানকি ওর ফাসি চাই। মনোযোগ দিয়ে দেখেন ওর সামনে ওর স্বামীকে কুপিয়ে মারে আর ও ঠান্ডা মাথায় ওর দুই ভাতারকে মেরে পাঠিয়ে দিয়েছিলো। ও একটা মাগী,1,crime
বাংলাদেশের কোন বাহিনী এবং ডিসির উপরে এবং মন্ত্রীদের উপরে জনগণের কোন ভরসা নেই কারণ তারা কুকুরের বাচ্চা মানুষ দেখলে ঘেউ ঘেউ করবে আর মানুষ না দেখলে চুপ করে থাকবে বলবে এটা আমি জানি না ভরসা শুধু আছে মহান আল্লাহ তা আলার উপর কারণ তিনি সব সময় বান্দার পাশে থাকেন,1,crime
শালারে পুইতালা শালারে,1,crime
এই মাগির পুরা পরিকল্পনা মাগির বোদার বিতরে গরম ডিম দেওয়া উচিত একটা ফুলের মত জিবন নসট করলো মিনির পাছার ভিতরে বাস দেওয়া উচিত,1,crime
সে এত বড় অফিসার তারকি এটা সাজে এজন্য বললাম সে একটা জানোয়ার আরজে ক্যামেরা করেছে তাকে ধন্যবাদ স্যালুট মেয় খারাপ অভিসার একটা বাইনচোদ,1,crime
শালির একটা দিয়া হয়নাই আরো টা লাগবো।,1,crime
কম হলে রাস্তায় জন পুরুষ ছিল। এ গুলা সব হিজলা। হিজলা বললে ও কম হবে।,1,crime
জুতা মার শালা‌রে,1,crime
রিফাতকে মারলো তোমরা দেখলা এইখানে জত গূলা ছিল কুকুরের বাচ্চা তোরা সবাই খুনিদের গ্রেপ্তার করতি ওখানে সবাই মিলে গন ধোলাই দিয়ে মাংস ভাগ দিয়া বিক্রিরি করতি,1,crime
হালার এ ইট বান্দা হোক।বানচোত,1,crime
হালার পুতরে বিচি থেতলিয়ে দে,1,crime
সালার লজ্যা নাই সালা আবার কথা বলে,1,crime
ওছি কুত্তা কোথায়,1,crime
মাদারচোদ পাবলিক শালারা চোদন মারছে ।,1,crime
এসব জানোয়ারকে পাবলিক এর হাতে তুলে দেওয়া হক কারণ যারা সমাজ রক্ষা করতে পাবলিক এর বিচার করবে তারাই এসব বাজে কাজে লিপ্ত তাদের বিচার কে করবে।,1,crime
সালার পুটকি দিয়া গরম ডিম দিলে সব সত্য কথা বাইর হবে,1,crime
স্যারের দোস নাই চোদা মনে হয় ভালো দিছে শালি মাগি,1,crime
এই মাগীর জন্য দুই জনকে মরতে হলো।,1,crime
সাওয়ার ভিডিও শুধু জরিয়ে ধরে থাকে কিছু করতে পারে না ডিসিরে কলিকাতা হারবাল খাওয়া,1,crime
এখনো কেন ফাঁসি না এই কুত্তার বাচ্চাদের,1,crime
ফাসি দে সালাকে,1,crime
ছি ছি শালা আবার ক্যামেরার সামনে এসে কি ভাবে কথা বলতেচে ছি,1,crime
ওই মাদারির বাচ্চারে জুতামার। ওরা আইনের নাম করে । বেআইনি কাজ করে। আর ধরা পরলেই কিছু জানে না।,1,crime
এমন ঘটনা বাংলাদেশে অহরহ ঘটছে যা আমাদের দৃষ্টিগোচর হয় না।এই লুইচ্ছা কে ঔ নারীর সাথে বিয়ে দেয়া হোক।,1,crime
এই মাগিরে রিমান্ডে নিয়ে যদী প্রমান হয়েই যায় তবে এই মাগিরে জনে ধর্ষন করে মেরা ফেলা হোক আর এই বিডিয় তে প্রমান হয়েই গেল সব ধূষি এই মাগি,1,crime
এই মাগির বুদায় এসিড মারা হোক,1,crime
আমারত ছিরা জুতা নাই থাকলে তাকে পিটাই তাম শালার হারাম খোর👠👠👠👠👠👠👠👠👠👠👠👠👠👠👠👠👠👠👠👠👠👠👠👠👠👠👠👠👠👠👠👠👠👠👠👠👠👠👠👠👠👠👠👠👠👠👠👠👠👠👠👠,1,crime
যেখানে ভিডিও তে সব ক্লিয়ার দেখা যাচ্ছে সেখানে আবার কিসের তদন্ত করবে ডাইরেক্ট বিচার করা দরকার ঐ শুয়ারের বাচ্চার!,1,crime
এগুলো সব মাদার চোদের ফাসি চাই আর পিছুনে ব্যাগ ওয়ালা ওইপিচচকে দরে ফাসি ঝুলানো হক।,1,crime
এই ভিডিও করছে তাকে সালে একুশে পদক এবং মেরিল প্রথম আলো পুরস্কার দেওয়া দরকার আমি তাকে নোবেল পুরস্কার দেওয়ার জন্য নোবেল কমিটির কাছে অনুরোধ জানাবোএমন লুচ্চাদের মুখোশ খুলে দেওয়া জন্য,1,crime
শালার বিচার চাই।।।।।।,1,crime
পুলিশ চুদার টাইম নাই খানকির পুলারা দেশটা নিজেদের মনে করে,1,crime
আর যাই হোক মাল টা কিন্তু সেই একদম চ্যাপটা ডিসি হালারপুত খাইয়া মজা পাইছে,1,crime
যত শব ছাগল পাগল,1,crime
মিন্নি খাংকি মাগি পুরাই দায়ী এই খুনের সাথে। এই ভিডিওতে স্পষ্ট বুঝাই যায়। ওর জামাইরে ধরে নিয়ে যাচ্ছে আর ও পিছে পিছে কি সুন্দর হেটে যাচ্ছে। তারপর নাটক শুরু করলো বাচানোর। কিন্তু মনে মনে ঠিকি বলতেছে আজ তুই মরবি। বাংলাদেশে এরকম খাংকি মাগির অভাব নাই। মাইয়া জাত বহুত খারাপ। এগুলারে ধরে আগে জেন্ত রাস্তায় পুরা উচিত। এরপর বাকি বিচার,1,crime
সালা লুচ্ছার ফাঁশি হওয়ার দরকার,1,crime
সর্বপ্রথম ঐ বেশ্যা নারীর কঠোর বিচার হওয়া উচিত মনে আমি মনে করি।,1,crime
সবাই জুতা মারো এই জানোয়ার ডিসিকে,1,crime
ভিডিওতে যেটা দেখলাম এটা সত্য এই কু ত্তার বাচ্ছা যে আরো কত মেয়ের ইজ্জত নষ্ট করে ছে তার নেই ঠিক সালার দেখতে পুরো সাধুবাবা এর প্রকাশ্যে জবাই করা দরকার,1,crime
মাগি আকাম করার সময় বাচ্চার কথা মনে ছিলনা।।।,1,crime
খানকি মাগি চোদাচুদির সময় মজা পাইছো আর টাকা পাইছো ঐ সময় ভাবোছ নাই তোর যে জামাই এবং বাচ্চা আছে । আমি মতে দোগো কোনো বাচার অদিকার নাই। আমি তোগো দুই জনের । আরব দেশের মতো শিরোচিত চাই লক্ষ্য জনোতার সামনে ।,1,crime
অর মেয়েরে এখন সবাই চুদ,1,crime
হালার পুতেরা স্যার স্যার চোদাস। যাইয়া শালার গালের উপর জুতা দিয়ে মার।,1,crime
আবে ছাগলের বাচ্চা সাংবাদিক কুত্তা মিনিট হবে না হবে মিনিট। বাকি মিনিটে কি হইছে দেখলে তুই নিজেরে ঠিক রাখবি না। ভালো করে দেখ।,1,crime
সব গাঞ্জা খোর মাগি খোর,1,crime
লুচ্চা চুদানির পুলা,1,crime
এটা নিয়ে মানুষ কেন এত বাড়াবাড়ি করছে আমি কিছুই বুঝিনা সুন্দরী প্রাইভেট সেক্রেটারি নিয়োগ দেওয়া হয় চচুদাচুদি করার জন্য তা না হলে ছেলেদের কি চাকরির জন্য অভাব পড়েছে নাকি,1,crime
এই বাংলার মানুষ যারা মজা দেখে খানকির বাচ্চাদের কি যে বলতে মনে চায় যা ভাষায় প্রকাশ করতে পারিনা।,1,crime
শালা কুত্তা শালা বান্দির পোলা তার মেয়েকে কেঊ চুদেনা কেন,1,crime
এই মাদার চুদ চুদা দোয়া আবার বড় কথা বলেস,1,crime
রিফাত নয়ন দুজনই একটি নির্দিষ্ট মাগীর গুদের প্রতি আসক্ত হয়ে পড়েছিল। পুরুষের যৌন ঈর্ষা এই রকমেরই ভয়ানক হয় যা মুন্নী মাগী এবং তার সর্বদা পিচ্ছিল যৌন গহ্বর সেটা উপলব্ধি করতে পারেনি। ফল স্বরূপ এই ঘটনা। মাগীটা শাস্তি না পেলে নতুন ল্যাওড়ার সন্ধানে থাকবে। আপনাদের কারুর সমসময় যদি ঠাটিয়ে বাঁশ হয়ে থাকে তাহলে সুযোগ সন্ধানী হয়ে উঠুন। সুযোগ আসবে চাষ করার। নোংরা দেশ বাঁড়া।,1,crime
খানকির পুলারে জালাইয়া মার,1,crime
জনের গায়ে আগুন দেয়া উচিত,1,crime
নয়ন খানকির পুতের ফাসি চাই,1,crime
খানকির পোলা এখনো মরনাই কেন আর ঐ মাগিই বা কেমনে বেচে আছে,1,crime
সালারে জুতা মারা দরকার,1,crime
হা হা হা হা হা হি হি হি হি সব কিছু সাজানো সিসি ক্যামেরা তে সেটা কি তুর ভুত। লুচ্চা বাদাইমা শালা বিয়াদপ নারী লোভি শয়তান জুতার মালা পরে উপস্থাপন করা উচিত সারা বাংলাদেশে এই সব বিয়াদপের জন্য আজ শতো শতো পরিবারের আগুন পরকিয়ার দাবালনের অসহায়ত্ব হয়ে ভেংগে যাচ্ছে শতো শতো সংসার এই বিয়াদপ পুরুষ এবং মহিলার কঠিন বিচার হওয়াটা খুবই জরুরি।,1,crime
স্যারের দোষ থাকবে কেন স্যারতো তোর সোনা পাঠাই দিছে মাগী তুদের মতো বেইশ্যা মাগীর কারণে এরা এসব করতে সুযোগ পাই।,1,crime
বোকা চোদা পাবলিক এক জনের সাথে থাকতে পারে বিয়ের আগে কতো কিছু করে মাদার চোদ নয়ন এতো মামলার আসামি কেন,1,crime
কিসের বিচার চায় নাটক করে। ডি সি আর এই বেশ্যাকে আদালতে নিয়ে জনসম্মুখে বিয়ে দিয়ে দিন। ঝামেলা শেষ । তারপর ঘন্টা ফ্রি স্টাইলে চলুক 😄😄😃😁,1,crime
স্যারে দোষ থাকবে কি করে। এই মহিলা তো সাগর কলা খাওয়া শখ হয়েছিল।আর স্যার কলা দিছে বিনা মূল্যে।মাগী কুকর্ম করার আগে সন্তানের কথা মনে ছিল না।,1,crime
মিননিকে আমি চোদে মারতে চায় বাংলার নেতাদের ও নেতার বউদের কে আমি চোদি বাংলার পুলিশ ও পুলিশের বউ দেরকে আমি চোদি বাংলার সরকারকে আমি চোদি কারন ওরা সবায় রংবাজ লালন পালন করে সবাই মিলে বাবা ইয়াবা গাজা খুন খারাপি সব ধরণের খারাপ কাজ করে,1,crime
এই খানকি এই সব করছে ওর মায়ের চুদি।,1,crime
সালার ধনে ইট বেধে দিতে হবে সালা জনগনের চাকর সালারা নিজেদের আল্লাহ ভাবা সুরু করেছে মানুষ কি গবর খায় এটা হেকার করেচে,1,crime
শুয়ারের বাচ্চার মাথা থেকে টুপি খোলে না কেন,1,crime
মিন্নী কুত্তার বাচ্চার ফাঁসি চাই,1,crime
ছিঃ মিন্নি! তোমার মতো স্ত্রীর জায়গায় একটা পতিতা থাকলে আরও ভালো উদ্যোগ নিতো তার সামীকে বাচনোর জন্য,1,crime
বলদা ভিডিও,1,crime
রংগরিলা করে এখন বাচার মত বাচতে দিন !!!! যখন এই দেহ ব্যবসা করেছ তখন বাচ্চাদের কথা মনে ছিল না !!! বেশ্যা,1,crime
ডি সি বদমাশ একটা কুত্তা বাচ্চা এই দারনে অপকর্ম করে জারা তাদেরকে সো নায় ইট বেদে ঢাকা শহরে ঘোরানো দর কার,1,crime
ভিডিওটি ফেসবুক থেকে নিয়ে নিয়েছি। শালার পুত এখন বলছে ওগুলো সাজানো!! হা হা হা!!,1,crime
মাগিরে নিগরো কুরু দিয়ে পুসদিলে সত্তি কথা বেরিয়ে আসপে,1,crime
পুলিশ হচ্ছে সবচেয়ে বড় মাদারচোদ,1,crime
সালা অমানুষ সালা কে কুত্তা পেঠা করার ধরকার,1,crime
এ সব হাসিনা সোনার ছেলেরা বতমান সরকারি অফিস গুলো পতিতা হয়েগে ছে,1,crime
এই লুচ্চার বিচার হবেনা,1,crime
আবাল একটা। নিজে আকাম করে অন্যের নাম দেয়। শালা কুত্তার বাচ্চা।,1,crime
এই খানকির পোলাকে ল্যাংটা করে পেটানো হোক,1,crime
মাগি,1,crime
চুতমারানি আবার বলে স্যারের দোষ নাই😃। চোদ্দা চোদ্দির আগে সন্তান স্বামীর কথা মনে ছিলো না। ডিসি বইলা কথা।চোদ্দলে চুতমারানি ☺ খুশি। জনগণ কি দুধু খাই।,1,crime
পাগল ছাগল তোদের কাহিনীর সাথে বরগুনার বাস্তব কাহিনী একদম অমিল সালা বরগুনার পোলা বাল বানাইছ কিছু জানো না লাফ দিয়ে উঠে ভিডিও বানাইতে গেলি রাম পাঁঠা গুলা,1,crime
মিন্নি সব জানে এই শালি ছেলেটা কে মারিয়েছে,1,crime
আহা! আরো কতো নাটক দেখাইবো। মিনিটের ভিডিওতে তো ভুদার জ্বালাই সব কাপরচোপর খুইলা ফেলছিলা তা এখন এতো নাটক চুদাউ কেন। যতই নাটক আর অভিনয় করো না কেন পাবলিক তোমার মতো খানকি মাগিরে থুথুও দিবো না,1,crime
চোদন বেশি পড়েগেছে।,1,crime
সাংবাদিক তোরা কি পাগল যেই মাদারচোদ আকাম করছে ঐ মাদারচোদের কথা বলিশ কেন,1,crime
খুশি হলাম জানোয়ারের বাচ্চাদের ফাঁসি হচ্ছে,1,crime
মাগিরে ডাইরেক ফাসি দিতে হবে,1,crime
এই খানকি মাগিটারে আমার কাছে পাঠাও। বেশ্যা কোথাকার!!,1,crime
সব জায়গায় ডিসির নাম কেন ঐ বেশ্যা মহিলাটার নাম নাই কেন এদেরকে ইসলামের নিয়মে শাস্তি দেওয়া হোক,1,crime
এই মাগিরে আমার কাছে পাঠিয়ে দেয়া হোক।,1,crime
এতদিন সাংবাদিক বাল ফালাইছে সাংবাদিক সব হল মালোয়ানের জাত ভারতের দালাল,1,crime
এ কেমন স্ত্রী যেকিনা স্বামী এতগুলো কোপ খাওয়ার পর ও নির্বিকারভাবে একা হেটে যেতে পারে। নারীবাদী হ ও বেশ্যাবাদী নয়।,1,crime
লুচা খানকির পোলা তুই তরে জুতা পেটা করা উচিত ছিল। আইনের লোক বেয়াই নি কজ করে এর কোন বিচার হবে মনে হয় না। এখানে তদন্ত করার কিছে ভিডিও আছে এটা ছবি না যে এডিএড করা এটা ভিডিও,1,crime
ডিসি বলতে ভুজায় ডিষ্টিক ইনছার্য সালা একটা জেলা কে কলঙ্কিত করেছে,1,crime
অই মাদার চোদ কে ফাশি চাই,1,crime
পুলিশের আস্কারা পেয়ে শালারা আরও বেশি লাই পাইছে আগে ধইরা পুলিশ নামে কিছু সন্রাস আছে ওদেরকে শায়েস্তা করা উচিত,1,crime
? যে মাগির বাচ্চাগুলা রিফাতরে ধরে নিয়ে গেছে ওদেরকে ক্রস ফায়ার দিলোনা কেন? বর্তমানে এরকম আরো অনেক মাগির ছেলে আছে যাদের ঘরের পিছনে বেড়া নেই আসছে রাজনীতি চুদাইতে। ক্লাস পাস করে নাই অতচ রাস্তায় হেটে হেটে সিগারেট চুদায়,1,crime
আমি প্রথম থেকেই জানতাম ঘটনার মুল হোতা মিন্নি মাগি অন্যের চুদা খাওয়ার জন্য রিফাতকে হত্যা করায় মিন্নি রিমান্ডে নিয়ে গিয়ে মিন্নির হেডা দিয়ে বড় বড় লোহার রট সিদ্ধ ডিম ঢুকালে সব বের হয়ে আসবে,1,crime
এই খানকি মাগির পোলা নডির পোলা কুত্তার বাচ্চা যে একটা লুচ্চা লমপট সেটা তার বাব বন্গিমায় বুঝা যাচ্চে মাগির পোলা তোরে পাইলে তোর ইট বেদে যুলিয়ে দিতাম।,1,crime
সাংবাদিকদের কোন কাজ আর নাই। সবার পাছাতে আঙুল দিতে হবে। যার সাথে ফিলিংস করছে সেতো খুশি ডিসি মহদউয়ের সাথে। আমার তো কপাল খুল গেল।,1,crime
ওই ডিসির মাইয়া থাকলেও ডিসির মাইয়ারে আমি চুদিবো,1,crime
কামুন নাটক করছে রানডি সালি মাগি মিননি আসোলে সব জানে মিননি জে আজ রিফাত কে খুন করবে নায়ন সব এই সালি নায়ন সাথে পরকিয়া পেম করার জন্য মিননি রিফাত কে খুন করাই ছে নাতো রিফাত কে জখুন মারার জন্য টেনে নিয়ে জাছিলো তখুন এই মিননি এদিক উদিক না দেখে মানুষ কে বলতো কি আমার সামি কে মারছে তোমোরা বাচাউ না বোলে সালি কুততির বেটি হাতে ডিজিটাল বাগ নিয়ে আসতে আসতে হাটছে তাই পুরা বুঝা জাই জে এই খুনে সমপরনো হাত এ মিননির কিন্তু রিফাত কে খুন করালি কানো রে রানডি সালি মিননি আল্লাহ তার ফল বুঝাই দেছে তৌকে অলপো বোইসে সামি হালা তুই রে মিননি রানডি মাগি তুই মুসলমানের মেয়ে হোয়া তুই পরকিয়া পেম করলি তাই আল্লাহ তালা তৌকে সাসতি দিলৌ রিফাত কে হারিয়ে,1,crime
সালার পাগল সহবাস না ইটাকে জিনা বলা লাগে সহবাস এক মাএ বোউয়ের সাথে হয়,1,crime
মাদার চুদের ভাব দেখকাই তো বুজা যায় ঘটনা সত্যি,1,crime
বেয়াদব মেয়ের বিচার চাই উপযুক্ত,1,crime
মেয়েতো চুদা খাওয়ার জন্য খুব অস্থির হয়ে আছি গো,1,crime
সব গোলা আবাল।,1,crime
খানকির পোলা মাদারচোদ,1,crime
ক্ষমতার অপব্যবহার উর্ধতন কর্ম কর্তারা এমনি লুচ্চা হয়ে থাকে এদের কঠিন শাস্তি হওয়া দরকার।,1,crime
আমি তোর মা বোনকে চুদি। সালা অপরাদ ঢাকার জন্য ভিডিও বানিয়েছে সালা মাদারচোদ,1,crime
কিছু জানোয়ারটা এইরকম ধরা ছেলে বলে,1,crime
হাসিনা সরকারের আমলে অফিসে আদালতে সাগরে বন্দরে এস্কুলে কলেজে গাডিতে বাডিতে টয়লেটে হালি চুদা চুদি কি সুরু হইয়া গেসে। এটাকি চুদা চুদির প্রতিযুগিতা চলসে। হাংকি মাগিরার পাডাত কি একজিমা হইসে। সামি সাডা যার তার লাটি দিয়া চুলকানি বন্দ করবা। আমি সরকারকে বলব আপ্নি কুরআনের আইন বাহির করে। মৃত্যু দন্ড দিয়া জাহান্নামে পাটিয়েদেন,1,crime
তুমি কান্দা চুদাও কেনো?? বাঞ্চোত তুই,1,crime
বেশ্যা মাগির !!! কঠিন শাস্তি চাই !!,1,crime
শালারে জুতা দিন বলে তধন্ত করছে বাংলা দেশের আইন ভালো না তা না হলে আগে জেলে নিত পরে সাংবাদিক ঐ খানে যাইত 😡😡,1,crime
মাগি,1,crime
সালাকে জুতা মার,1,crime
সানজিদা অফিস সহকারী হলে কি হবে খুব সেক্সি আছে তাই এই ডিসি নিজেকে নিয়ন্ত্রণ করতে পারে নি,1,crime
আরে শালী কে ধরছো না কেনো এক নাম্বার আসামী এই শালী তাকে ফাসি দে দেরি কিসের,1,crime
কুখ্যাত ভোট চোর কুখ্যাত নির্লজ্জ বেহায়া কুখ্যাত সন্ত্রাসী খুনি কুখ্যাত স্বৈরাচারী হাসিনার আইনের ধরণ দেখলে মনে হয় আমরা দাজ্জালের হাতে বন্দি যে অপরাধী তার সন্ধান নাই যে অপরাধীর মুখোশ খুলে দিল তার সন্ধানে আইন ব্যস্ত তাই এই রকম আইনকে আমি পুটকিও মারিনা,1,crime
মাদারচোদের আইন,1,crime
সালা চুদবে অফিসের নারী আর ওর বউ মেয়েকে চুদবে অন্য লোক জনে সালা কুত্তার বাচ্চা ৷৷৷,1,crime
মইরা যা মাগী।।।,1,crime
লুচ্চার বাচ্চার চুনু কেটে হাঁসকে খাওয়ানু হোক,1,crime
আমার সোনার বাংলাতে এমন রক্ষক নামের ভক্ষকের কোন জায়গা হবেনা।মাননীয় প্রধান মন্ত্রীর কাছে এর দৃষ্টান্তমূলক শাস্তি দাবি করছি।যেমন এই শালাকে এমন শাস্তি দেওয়া হোক যা দেখে অন্য কোন মানুষ যেন এমন অন্যায় করতে না পারে।,1,crime
বরগুনার কলেজের সামনে দাঁরানো মানুষগুলো আসলে হিজরা এতগুলা মানুষের সামনে একটা ছেলেকে এইভাবে মারল কেউ এগিয়ে গেলো না সব হিজরা সালারা।,1,crime
মাদার চুদ কত টাকা খাইছস মিন্নি মাগির পক্ষে কথা বলার জন্য,1,crime
এরাই হাসিনার সোনার ছেলে। না হলে হাসিনা মাগী ক্ষমতায় থাকবে কি করে।,1,crime
নানা আমি বিয়া করমু নানা বলছে বিয়া করবা নানু ভাই আচ্ছা ঠিক আছে এক কাজ কর নানু ভাই তোমার নুনুটা তোমার পুটকির মধ্যে গিয়ে লাগেনি দেখ নানু ভাই চেক করে বলছে নানা লাগেতো নানু ভাই লাগলে তোমার টা তোমার পুটকির মধ্যে দিয়ে বসে থাক বিয়া সোদান লাগতনা,1,crime
বাইনচোদ এগুলো সব সালা অশিক্ষিত 😡😡😡😡😡,1,crime
শালা কুওা জুতা মারেন সবাই তারে,1,crime
এই জানোয়ারদের ফাঁসি দেখার অপেক্ষায় আছি,1,crime
আপনাদের কান্না করে কি লাভ কোন লাভ নেই জানোয়ারদের সাজা পাওয়ার অবশ্যই দরকার জিন্দা মানুষ পুড়িয়ে মারার সময় তাদের খেয়াল ছিল না যে আমাদের পরিবার আছে ছেলে সন্তান মা বাবা আছে এখন ছেলে মেয়েরা কার পরিচয় দিয়ে রাস্তায় বের হবে মনে হয় মীরজাফরের চেয়েও খারাপ হয়েছে,1,crime
বাংলাদেশ সরকার বাল ফালাবে।সরকারি আওয়ামিলিগ এর কুত্তা তাই সরকার কোন বাল ই ফালাবে না তা জানা কথা,1,crime
শালির চেহারার কি অবস্তা হয়েছে এখন!,1,crime
হায়রে লুইচ্চার বাচ্চা,1,crime
জয় হোক কুত্তালীগের,1,crime
ধরা পড়ার পর সব মাগিরা এটাই বলে,1,crime
মাগি জানতো সবকিছু মাগি ভাবতে পারে নাই রিফাত মারা যাবে এটাই সত্য কথা,1,crime
বেয়াদব মহিলা জঘন্য ঘরে সামি সন্তান রেখে আকাম করে বেরাই,1,crime
হিজাব খোল।,1,crime
মিথ্যাবাদী খানকী মিন্নিকে ফাঁসি ওেয়া হোক,1,crime
ভাই ডিসির দোন আছে এ তো চোদার এস্টাইল জানে না যা মাল ভাই ঘোড়া চোদন দিতে হবে 😂😂😂😂,1,crime
তার দুন কেটে দেওয়ার দরকার,1,crime
বোকাচোদারা ভিডিও বানাতে পারো না কিন্তু আন্দাজ ভিডিও ছাইড়া দাও নাকি শালার পুতেরা,1,crime
ঐ জানোয়ারেরা জখন ও কে ফুড়িয়ে মারছিল তখন ওর মা বাবার কাছেও এমন ই লাগছে,1,crime
এই মিন্নি মাগিরও দোষ কম না। মাগির শাউওয়াতে মরিচের গুড়া দে,1,crime
এফডিসি র নায়িকা নয় ছোট্ট পর্দা র গায়িকা নয় বিশ্ববিদ্যালয় র ছাত্রী নয় অবশেষে পিয়ন চুদলি! তোর বাব দাদারা কি পরের বাড়ির কামলা খাটতো আর তোর মায়েরা কি পরের বাড়ির ঝী র কাজ করতো,1,crime
কুত্তার বাচ্ছাদেরকে লিঙ্গ কেটে ডিজিটেল বাংলার ডিজিটেল সম্ম্াননা দেওয়া হোক।,1,crime
দুই মিনিট চোদে শাল্লা হিজড়া,1,crime
পাপ বাপকেও ছাড়ে না। কুত্তার বাচ্চাদের প্রকাশ্যে জুতা পেটা করা উচিত।,1,crime
এই বেশ্যা মাগী লজ্জা নেই তোর,1,crime
জানুয়ার কাকে বলে এরাই তার প্রমান,1,crime
আমি পাসি চাই মাগির বাচা,1,crime
এই লোক তো জোর করে ওই নারীকে কিছু করে নাই তাই না তাহলে এই লোক শুধু কেন একা অপমানিত হবে।ভোঁদার জ্বালা তো ওই উচ্চ শিক্ষিত মহিলা ও মি টাই ছে আসলে বাংলাদেশ থেকে নারী শিক্ষা আর নারীদের চাকরি করার প্রথা টা তুলে ফেলা দরকার।বর্তমান সমাজে নারীরা আর মা জাত আর নারী জাত নাই তারা হয়ে গেছে উচ্চ শিক্ষিত নামের এক মাগি।,1,crime
এই মাগী সব আগেই জানে কি হবে সিসিটিভি আছে তা ও জানে অবশ্যই ডিসির এ অবস্থা হাওয়ার জন্য করছে অনেক টাকা ও পাইলো।,1,crime
মিথ্যাক সালা।।।,1,crime
হুম আমরা চাই মিননির ফাঁসি হোক মাগি একটা নরতোকি মিননির ফাঁসি চাই চাই চাই চাই চাই,1,crime
না চুদলে আর কি হইলো,1,crime
এই ডিসি কুত্তাটাকে চাকরি বাদ দেয়া হউক আর সাস্তি দেয়া হউক,1,crime
খানকি মাগি তোকে তো একটা কোপ দিলনা। তোর যদি এতই কোর কোরানি তুই বিয়ে করলি কেন? বিয়ের আগে কলা খাইছ সে মজা বাদ আরেক ছেলেকে তুই খানকি। তোকে জিজ্ঞাসা করলে সব বের হবে। ওকে রিমান্ড নেওয়া হোক,1,crime
হা হা হা বলদ,1,crime
মানুষ নামে জানোয়ারগুলো দাঁড়িয়ে তামাসা দেখছে । একটি লোক ও কি ছিলো না এই পশুগুলোকে বাঁধা সৃষ্টি করতে ? হায়রে আমার সোনার বাংলাদেশ !!!,1,crime
শালা ডিসি তুই চ করব আর মানুষকে দেখাবো,1,crime
একটা বলদ খালি চুম্মা করিয়াছে ভদার জালা মিটাইয়া দেয়নাই,1,crime
এরে জে চুূদলো সে ভাল জে ভিডিও করলো সে খারাপ আমার মনে হয় এ মাগি তাহলে কি অফিসে এখন মাগিও রাখা হয়।,1,crime
শালার ধোনে ইট জুলাও,1,crime
মজা কি খালি ডিসি পাইসে ওই মাইয়া পায় নাই।চাকরী দিসে দেইক্ষা শরীর দেয় যারা তারা পতিতা।সবাই ডিসির দোষ দিচ্ছে আর ওই মহিলাটা সাধু।দুনিয়াটা এমন যেখানে ছেলেরা কিছু করলে অপরাধ আর মেয়েরা করলে পরিস্থিতির শিকার। আর ডিসি যেটা মন চায় সেটা করুক এটা ওনার পার্সোনাল ব্যাপার। এটা নিয়ে নাক গলানোর দরকার নেই।ডিসি ছাড়াও এদেশে লক্ষ লক্ষ নারী পুরুষ এসব কাজে জড়িত।,1,crime
কোন বালের মাথা বুঝাইলেন ভাই,1,crime
মাগির সাথে মাগার কুত্তার যেমন পেচিয়ে থাকে মানুষ দেখে লজ্জা পায়।ঠিক সেভাবে মাগার লিংগ মাগির বুদার ভিতরে আটকিয়ে রাস্তায় দাঁড়িয়ে করে রাখা হোক,1,crime
এই৷ খানকি মাগিকে ফাঁসি দেওয়া৷ হক,1,crime
লুচ্চামি করছে এখন গাঢাকাদে লুচ চা হারা মি,1,crime
দৌড় দিলো কই ভিউস পাওয়ার জন্য তোরাও এগুলা ক্যাপশনে দিস বাহ চুদির ভাই বাহ 😑,1,crime
খ।নকির পোল। ম।গির ব।চচ। তোর ম।রে চুদ তোর বনেরে চুদ,1,crime
শালার বন্ড গ্রুপ পাইলে একটা একটা করে ধরিয়া হাকি ওলা বাশ পাছা দিয়া ঢুকিয়া মৃত্যুর টিকিট হাতে ধরাইয়া দিতাম।,1,crime
অগরে চুদে মেয়ে গূলোকে,1,crime
প্রত্যেকটায় এমন মাদারচোদ খানকির পুলা ওগো কিসুই হইবো না জানা ই আছে,1,crime
নুনু খারাইছিলো তাই করছে ॥ সরল মনে অন্যায় করছে এত বলাবলির কি আছে,1,crime
লুচ্চার বাচ্চারে গণ ধোলাই দেওয়া দরকার ছিলো ।,1,crime
সে নিজেই নাকি তার অপকরমের তদনত করবে।অারে কুওা তুই বিষ খেয়ে মর।,1,crime
মাগির ছেলেদেরকে আজকে ফাঁসি দেওয়া হোক মেয়ে দেরকে আগে,1,crime
জয় চোদাচুদির জয়,1,crime
মাননীয় স্পিকার ডিসিকে ইন্ডিয়া পাঠিয়ে হারবাল ডাক্তার দেখানোর অনুরোধ হুদাই মিনিট সময় নষ্ট করলো। টিসু না থাকলে বন্যায় সব বেঁসে যেতো। মহিলাটি পেন্টি খুলেছেন কিন্তু হিজাব খুলেন নি বাহ বাহ পাওয়ার যোগ্য। মিনিট কে কে দেখলেন,1,crime
সামি কে দরে মারে বউ কি সুন্দর করে পিছনে হাটে এই মাগির কারনেই রিফাত মরচে,1,crime
আহা কি সুমধুর গান যা শোনলে কুকুর ও পালাবে শালায় জাতীয় বদমাইশ 😏😏😏,1,crime
প্রতিমন্ত্রীকে ভিডিও টি দেখানো উচিৎ। তাহলে আর তদন্ত দরকার হবে না। শালার পোলা ভিডিও থাকার পরও তদন্ত দরকার।,1,crime
অরে হাতি দিয়ে চুদান তাহলে মিন্নির শিক্খা হবে রিফাত বাইয়ের আত্তা শান্তি পাবে আমি গরিপুরের হাবিবুল্লা,1,crime
খানকিরপোলা ডিসি মেয়েদেরকে চাকরি দেওয়ার নামে লুচ্চামি হালার পো এখন ধরা খাইছে কত রকম অভিনয় করে খানকির পোলা লুচ্চা হালারপুত🤛🤛💄,1,crime
কোথায় ডিসির মুখ তো দেখছিনা তবে তার বদনাম করছো শালা শয়তানের বাচ্চা,1,crime
সালা গ্রামের সন্মানটা নষ্ট করতেছস,1,crime
পাগল ছাগল গুলো,1,crime
পর্ণ তারকারে চাকরি দিলো কেমনে,1,crime
আমার পথম থেকে সন্দেহ এই মাগির কথা বলার দরন দেখে৷ এই মাগির চোখ দেখে বুজা যায় এক পুরুষে সন্তুষ্ট নয়,1,crime
মিন্নকে তাইরে তেল দিয়ে ভালো করে মালিশ করে চুদলে ভালো হতো তাইর বিশ কতটা দেখতাম,1,crime
ডিসি তর বউ ত কত সুন্দর কালো হলে কথা ছিল সালা লুচ্ছা মেয়ে দেখলে জিব্বা নরে চারদিনের চোরা একদিনে দরা,1,crime
কুত্তা শালা,1,crime
শালাপুতেরা কেরোসিন তৈল তোর কোন বাবা কিনেছে। আবার বলিস এটা আত্ম হত্যা। জানোয়ারের বাচ্চা তোরা সবাই। মাদরাসাতে বসে এমন করিস।,1,crime
মাগিরে ভালো করে চোদা দিলে গেয়ান ফিরে পাবে,1,crime
এরকম করে নুসরাতের পরিবার ও একদিন কান্না করে ছিল তোদের জন্ম দেওয়া কুলাঙ্গার সন্তানদের কারণে,1,crime
ছাগলের বাচ্চা ডি সি পাগল হইয়া গেছে লুইছচা,1,crime
খানকির পোলা কে জুতা দিয়ে পিটানোর দরকার,1,crime
হালার সোনা কাইটা দেয়া উচিত নটির পুলায় এই ঘটনাও অস্বীকার করতেছে!,1,crime
বালের কথা ছাড় কিছু না,1,crime
পুরা পাক্কা খেলোয়াড় এই দুই মাগী ম খানকিমাগী তই নিউ তোর ভোদায় নিউ সোনা ই ভইরা দিতে হইব,1,crime
কি বালের নিউজ করিস বাইনচোদ তোর বাবা ডিসি অফিসে বসে এই অনৈতিক কাজ কেন করলো। তোর বারা ডিসির পিঠের কুকুরকেই খাওয়ানো দরকার।,1,crime
খানকির পোলা মন্ত্রী দেখস না ডিসি চুদাচুদি করছে। আবার তদন্ত কি দেখেও কি দেখস না।,1,crime
বিয়াদপ গুলো যখন্য কাজ করে মা বাবার কি কষ্ট দিল।এই সব কাজ করার আগে মা বাবার কথা চিনতা করতে হয়।সালির ছেলেদের দ্রুত ফাসি দেওয়া হোক।,1,crime
মিয়া খলিফার বড় বোন মাগি তুই 🖕🖕🖕,1,crime
চুদা নিতে পারবেনা তাই,1,crime
ডিসি শালা একটা কুংলাগার সন্তান শালা আইনের লোক হয়েও বেয়ানী কাজ করছে এইসব কুংলাগার সন্তান কে ফাঁসি দেওয়া উচিত,1,crime
আজ যদি সাধারন জজনগন এটা করতু আর ভাইরাল হত গন ধোলাই দিয়ে জেলে দেয়া হত আসলে সাধারণ জনগন এগুলো করেনা করেতু সব বড় বড় নেতা খেতারা তাদের ক্ষমতার জোরে আরো না জানি কত কি করে মুখোসের আড়ালে সালা আবার ডিসি ছি ছি ছি 😠মাগীটা আবার বলে সারে আমার খতি করেনি মাগী,1,crime
মাগির ভোদার ভিতোর রড দেয় না কেনো,1,crime
সাব্বাশ খানকির ছেলে,1,crime
অপিসের মেয়েদের না চুদে তুর মারে গিয়া চুদ তুর মা খুশি তুই ও খুশি,1,crime
মাসুদা ভাট্টি মুন্নি সাহা কই মাগিরা এখন চুপ কেন,1,crime
ঐ শালী কে ধরে আইনে আনা হোক। মাগির পুত কে ধরে লেজ গেটে দেয়া হোক,1,crime
কুত্তার বাচ্চা।। ভদ্র লোকটার কোন দোষ নাই।। তুই মাগিদের মত আচরণ করছিলি।। তোদের মত বেলাজ যতদিন দুনিয়াতে থাকবি ততদিন অনেক মানুষ কে চরিত্রহীন হতে হবে। মেয়েটার কন্ঠ শুনেই বোঝা যাচ্ছে খুব অল্প শিক্ষিত মেয়ে।। এই জন্যই মেয়েদের কে কাজ করতে দিতে নেই।। তারা সুযোগ পেলেই কুকরমে জরিয়ে পরে।। মাবুদ আমাদের হেফাযত করুন,1,crime
সালা আকাম কু কাম কর। আবারও বড় বড় কথা,1,crime
আমি আগেও বলেছি এখনো বলছি সব দোষ মাইয়াডার যে মারছে বা রিফাত খুনি যাকে পুলিশ ক্রসফায়ার করে মারছে তার কোন দোষ নেই আমাদের দেশে হাজারো প্রেমিক আছে যাদের বুকে সারাক্ষণ প্রেমে দাগার আগুন জ্বলে তারা বর্তমানে নেশা গ্রস্ত তারা বুঝবে যে মারছে সে ভাল করছে এদের জ্বালিয়ে কয়লা করা উচিৎ যেনে শুনে অন্যর প্রেমিকা কে কেন বিয়ে করে? তাগো মাইরে চুদি হেতিরা অন্ধ মাগির পুলারা মাইয়াডার দোষ দিয়া এখন আর লাভ নাই সে ও প্রেমে অন্ধ ছিলো বুঝতে পারেনাই সে এতো কিছু ঘটবে,1,crime
তোর স্বামীর সাথে ধোকা বাজি করছো এর বিচার তো তোমাকে পেতে হবে তবে তোমার একটা প্রশংসা করতে হয় তুমি তোমার প্যান্টি খুলছো কিন্তু হিজাব টা খোলেনি হিজাব এর প্রতি সম্মান দেখাইছো মাগি একটা তোর হেডার ভিতর আইক্কাআলা বাঁশ ঢুকাইতে হইবো,1,crime
লুচ্চা ডি সি তার ফাঁসি চাই।,1,crime
বাল হালা দরা কাই চে।।।। চা ডেলে দেউ,1,crime
ফাসি দেওয়া হউক চোদারনির পুলারে😡😡,1,crime
আরে ভাই ! তোমার প্যাসাল থামাও। এ সব শুনতে চাই না। লম্পট লুচ্চা ডি সিকে ধরে ওর লিঙ্গটি কেটে ফেলো। আর সাধনা মাগীকে ধরে উলঙ্গ করে ওর বোদায় গরম লোহার রড ঢুকিয়ে দাও। বোদার চুলকানিও কমবে কিছুটা মজাও পেতে পারে। এরা জাতির কুলাঙ্গার এবং সমাজের ক্যান্সার।,1,crime
মাগী চোদা দিতে ভালো লাগলো,1,crime
সালার ধন কাটাইয়া দে,1,crime
সে চুদাচুদী করছে এখানে হ্যাকার কি করছে হ্যাকার কি ওরে কোনো বাবার বড়ি খাওয়ায়া দিসে যার কারণে হালা হুশ হারায়া মাগী লাগাইসে!!,1,crime
মিন্নি মাগিরে রিমান্ডে নিলে সব তথ্য বের হবে আমি সিওর,1,crime
খানকির পুতরে বহিসকার করে নাই কেনো সরকার,1,crime
কিয়ামত বেশী দুরে নেই রে ! হারামজাদা রা !😩😩,1,crime
মাগি ছেহারা দেখলে কি সমাস বাস্টার্ড,1,crime
মুক্তি যুদ্বারা দেশকে চুদে দাও। ও মুক্তিযোদ্ধারা,1,crime
ডিসির এই দালালকে কুততা দি চুদা হেক,1,crime
মাগি তখন মনে ছিলোনা তুই তো মিয়া খলিফাকেও হার মানাবি,1,crime
মিন্নি সহো ঐ সব জানোয়ারদের ফাঁসি চাই,1,crime
দেশি কুকুর লীগ সবচেয়ে খারাপ এবং লুচ্চা এবং চোর আওয়ামী লীগ দলটির একটি নিকৃষ্ট দল এদেরকে সারা জীবন লজ্জা শরম হবে না,1,crime
চাকরি চাইতে গেলে ছেলে লাক্ষ ঘোস চায়। মাইয়া হলে ফ্রি চাকরি ঘোস লাগে না। কাহিনী চোদন চোদন এর জন্যই ওদের চাকরি হয়। ছেলেদের হয় না। মাধার চোদেরা তোদের কারণে আজ ছেলেরা বেকার ঘুরে আর নেসা করে বেড়ার,1,crime
চুদতে ভাল লাগে,1,crime
লুচ্চা হাতে দেশে চালানো কি ঠিক,1,crime
মিন্নি মাগিরে রিমান্ডে নিলে সব বেড় হবে ওর সাজানো সবকিছু সেটা ওর চলাফেরা দেখলেই বুঝায় ওর শামিকে ধরে নিয়ে যায় মারে আর সে রিলাক্সে হাটছে সবার পিছনে এটাতে কি ক্লিয়ার নয় মিন্নি জরিত আছে মাগিরে রিমান্ডে নিলে সবকিছু বেড় হবে,1,crime
আল্লাহ ওদেরকে দুর্যোগবাশি করুন আল্লাহ ওদেরকে কখনোই ক্ষমা করবেন না ? কুকুর বাচ্চা ???,1,crime
লুচ্চা প্রশাসক,1,crime
মেয়েটাকে তো রেপ করেনাই মেয়ে ইচ্চে করে খেলা দিছে এমন ইচ্চে করে খেলা দিলে কে ছেড়ে দিবে আমার তো মনে হয় এই কুত্তার বাচ্চার কোনো দোষ নাই😏,1,crime
খানকির পোলারে জুতা দিতে পিডানোর দরকার। ভিডিও ফুটেেজ সব পরিষ্কার হয় গেছে আর সালা নাকি এইটা তদন্ত করবে।,1,crime
খানকীর পোলা মেয়ে চুদবা আবার মানসিক বিপর্যস্ত চুদাও।।।এই ধরনের ডিসি কে দেশ থেকে বের করে দেওয়া উচিত।।।সালার বদমাইস।।।বুরা ভাম বাড়িতে বৌ থাকতে অন্য নারী চুদিস।।।তোর বৌ তোর নুনুটা কেন গুড়া মেরে কেটে দিচ্ছে না এইটাই বুঝলাম না।।।একজন আইনের কর্মকর্তা হতে হলে ভাল হওয়া চাই আর তোর তো ই নাই।।।সালার বুড়া ভাম বসমাইস।।।।আমরা দেশবাসী এমন কুলাঙ্গার ব্যাক্তির শাস্তি চাই ।।,1,crime
কুত্তার বাচ্চা ☺,1,crime
এর ভিতরে কোন অনুশোচনা নেই এই খানকিটা আসল খুনি এ খানকিমাগী কথা বলতেছে কোন শোক নেই ন ওর ভিতরে মাঝখানে কিরে খাওয়া উচিত,1,crime
তার স্বামীকে ধরে নিয়ে যাচ্ছে উনি কেউ কে ডাক দিলো না কিছু বলল না ওই মেয়েটা এক নম্বর শয়তান লম্পট,1,crime
মাদার চুদে কয়কি ভিডিও বানায়চে,1,crime
খানকি মাগি বলে কি চোদা দিছত আবার বিচার ছাস এই সব মাগিদের কারনে আজ বাংলাদেশটা ধংসের পথে,1,crime
মাগী সরম নাই আবার বলে স্যারের কনো দোষ নাই।খানকি তোর জন্য ভালো মেয়েদেরও বদনাম।।,1,crime
আমার জীবনেও দেখিনাই🙄 অফিসের ভিতর খাট ।🤔 তার মনে বোঝর বাকি নাই লুইচ্চা ডিসি । আর কি ছু মাগিও আছে ঘরে ভাতার রেখে পরপুরষের সাথে ফষ্টিনষ্টি করে😡,1,crime
মিন্নি হলো পতিতা আর বাংলাদেশ আন্তজাতিক পতিতালয়,1,crime
বালের বিচার করে,1,crime
সালা ঠিকমতো কিছুই করতে পারলনা হিজরা আমি হলে শুধু ছুদা চুদী চুমাচুমি ছাড়া,1,crime
শালায় ঘরে হরিণ রেখে জংগলে শূয়র খাইতে গেছিলো।,1,crime
ছাগলের বাচ্চা এডমিন এইগুলি নাকি নুসরাত হত্তার আসামি,1,crime
ওফু আমার মাথা গরম হয়ে গেছে মাদারি রে যদি আমি একবার সামনে পাইতাম ঠিক এভাবেই কোবাইতাম।,1,crime
মিন্নী তো একটা মাগি আইটেম এর মেয়ে,1,crime
আহারে দুঃখে চুদনা হয়ে গেলাম নিজের তদন্ত নিজে করবে 🤬,1,crime
ভোদার ডিলার,1,crime
শালাকে লুচ্চা লুচ্চা লাগে। আবরা বলে সে নিজে দেখতেছে,1,crime
এই খানকি সব সময় ডিসির পাওয়ার চোদাইতো অফিসের লোক গুলোকে নাকি মানুষ ই মনে করতো না। একটা পতিতা।,1,crime
সব দুষ এই মাগির বাচ্চার,1,crime
মাগি মিন্নি জরিত,1,crime
ছিঃ মাগি ছিঃ,1,crime
মাগি তুই এখন পতিতালয়ে বাসা ভাড়া নে,1,crime
এইসব হাংকি মাগিরা নারি নামে কলংক তাকে গরম ডিম দেওয়ার দরকার।।।।,1,crime
জে সালারা বিডিও দেখছে সব সালার চোখে ওল পাপরি হইছে কানা চোদার্,1,crime
তুই মোরে যা তোর সন্তান ওর বাবা দেক বেনে দুর চিরতা মহিলা,1,crime
বাইন্চুদের বাচ্চা কি ভাব নিয়ে কথা কৈতাছে মনে হৈতাছে হেতে ভাজা মাছ টাও উল্টিয়ে খাইতে পারে না,1,crime
মাগী তুর ভোদার ভিতরে বাঁশ দেওয়া উচিত তোকে চুদব নষ্ট মাগী ।,1,crime
সালা লুচ্ছা আবার বড় গলায় কথা বলে।,1,crime
যারজ মাদারীর চোদ,1,crime
দিনের মত পরিস্কার এই গটনাকে এখনো পশুর বাচ্চারা বলতেছে আত্যহত্যা আর পরিবারের লোকজন খুশি হওয়ার কথা এইখানে কেন কান্না করে ওরা,1,crime
এই কুকুর বাচ্চা৷ চাকরি না৷ পা সরকর৷ কাছেদাবি করলাম,1,crime
ভাব চুদাই সালাই,1,crime
এসব জানোয়ারদের ফাসি হোক,1,crime
এইটা জামায়েত শিবির ও বি এন পি র হাত আছে।। শালা বাইন চোদ,1,crime
শালা তো জামালপুররে খেয়ে দিলো😍 শালারে কাছে পাইলে আমার পোষা কুকুর দিয়ে পুটকি মারাতাম,1,crime
লুচ্চা ডিসি,1,crime
সালার উপযুক্ত শাস্তি দাবি করছি সালারা দেশকে ধংশ করে দিচ্ছে,1,crime
সালারা চুদার সময় মাথা ঠিক থাকে।আর ধরা খেলে বলে ভুল হয়ে গেছে।আজ গরিব কেউ ধরা খেত তাকে জেলে দিত।,1,crime
বিচার দুজনের হবে ওই শালা এত এরকম কেন করল আর এই চুতমারানি এরকম কেন করলে হবে যাবজ্জীবন কারাদণ্ড তা না হলে ফাঁসি আর জেলখানার ভিতরে তাদের দুজনকে একসাথে দিবেন আমি দয়া করে বলবো মিডিয়াকে এ কথাগুলো তুলে ধরার জন্য সো স্যাড হায়রে বাংলাদেশ,1,crime
সন্ত্রাসির নাম নয়ন ছিলো সোহেল ছিলো না। মাইন্দারের বংশ মফিজের দল বাল বানাইছে,1,crime
সরকারে বাল ফালাইতে পারবো পরে যেই সেই হয় কোন বিচার নাই দেশে🙏🙏🙏🙏,1,crime
মানুষ পাগল না। সব সালা নষ্ট,1,crime
কে ভাইরাল করেছে সেইটা বড় কথা না। ওই খানকির পোলা এমন কোন করেছে সেইটা বলেন।।ওদের কাছ থেকে কি জাতি এইগুলা আাশা করেন। সালা হারামির জাত,1,crime
লুচচা আর লুচচার সাথে কে বসে আছে ভাই,1,crime
ঐ মাগিরে তো মরাই উচিত ভাতার চারে নাঙ্গের সাদ নিতে গেছিল বেচারি সাধনা,1,crime
মেয়েতাটো কাইলা ভুত কানকির পোলারা,1,crime
খানকির পোলারে ক্রসফায়ার কেনো দিছে অরে আমার হাতে তোলে দেয়া উচিৎ ছিলো,1,crime
জানোয়ারগুলারে এদের সামনেই কুকুরের মতো গুলি করে মারা উচিৎ,1,crime
সুয়ারের বাচ্চারে জুতা মার।,1,crime
শালারে লাথি মার পাচায়,1,crime
জুতা মারা দরকার খানকির পোলা পুলিশ কে,1,crime
জুতা দিয়া পিডাইয়া শালারে লক্ষী সারান লাগে,1,crime
এই কুত্তার বাচ্চার পা কেটে কুত্তাকে খাওয়ানো দরকার চেরে দিলে খারাপ হবে।,1,crime
হে হে হে বেটা কি বলে অপরাদীদে প্রশ্রয় দিতিরা হা সালা বাংলাদেশের কুটি মানুষ অপরাদী আর তুমি রিপটার সালা বলতেছোস মিন্নী কেনো দেস নাই হা ?,1,crime
মোল্লা মাদার চুদে রে আগুনে পুড়ে মারা হক,1,crime
এটা আর একটা বড় বোদার মাগি। গোড়ারটা হলেও কম হবেরে ভাই,1,crime
শালাকে জুতা পিটা করতে হবে।,1,crime
খানকীর বাচ্চা মিন্নী কে ফাঁসি দেওয়া হোক,1,crime
অফিসে সুন্দর সেক্সিদের চাকরি দেওয়া হোক যাতে চুদতে পারা যায়,1,crime
খানকিমাগী বলে কি ওদের জন্যই আজ দেশটা করুন অবস্থা,1,crime
এমন কিছু পতিতাদের কারণে শান্তির সুখের ঘর ভেঙে যায়।এই পতিতাকে এমন শাস্তি দেয়া হোক যেন তা দেখে অন্যরা শিক্ষা নিতে পারে ছিঃ কত নোংরা,1,crime
এই লুইচ্চা কে অতি দূত চাকরি থেকে বাহির করে দেয়া হোক যদি না হয় তবে বুজবো এইটা ও আওয়ামীপন্থী পুলিশ,1,crime
বাল সব নেশা খোর,1,crime
আরে মাগী তোর জিনিস তো সবাই দেখেছে তোর আর বেচে লাভ কি,1,crime
আর খতিয়ে দেখার কি আছে🤣🤣সব তো পরিষ্কার আর বাইঞ্চুদ ডিসি এখনো বলতেছে যে এটা সাজানো ভিডিও🤣🤣,1,crime
বাইনচোদের ছেরিরে এইভাবেই লাগাবো,1,crime
লুচ্চা মাগী দুই জন অপরাধী,1,crime
এই শালারা যদি লুচ্চামি করে তাহলে মানুষগুলোর কি করবে এই হারামি বুক ফুলাইয়া কথা বলে,1,crime
তোমার সাফাই গাওয়ার কারন কি তুমি মাঘির দালাল।তমি বিষয় নিয়ে চিন্তা করছো কেন লুইচছার পরিবার এর সন্মান কিষের। তুমি হুমায়ুন ডিসি কে বাঁচানোর চেষ্টা করছো। আসলে তুমি মাগীর দালাল। ডিসিদের এরকম মাগীর দালাল সব সময়ে থাকে। চুরির টাকা ভাগ করার জন্য খাস কামরা।তুমি ক্যামরা কে বসাইছে সেটা নিয়ে ব্যস্ত।তুমি তাঁর পুর্বব্রতী কর্মস্থলের দালাল ছিলে। কত টাকা নিয়েছ তার থেকে। একজনমুক্তি্যোদ্বা।,1,crime
সব দোষ ওই খানকি মাগির ওই খানকিক নাইজেরিয়ার হোল দিয়ে চোদা লাগবে ওই মাগির পোকা তাহলে ঠান্ডা হবে হামার কাছে হোল আছে লাগলে হামরই সার্ভিস দিবো ???,1,crime
মাদারচুদ মহিলা মিজিয়া তোমাদের বাবার খাইয়া আইছে,1,crime
ভাই তুমি দশ টা খুন করো কোন সমস্যা নেই শুধু বলতে হবে তুমি কুত্তা লিগ সব মাফ হয়ে যাবে হাইরে হাসিনা,1,crime
একটা হিজরার যতো টুকি দাম আছে। এই মানুষ নামের কুওার ছাওগো দাম দেওয়া ঠিকনা এরকম অমানুষ পাবলিক।আর যে নটির পোলারা মারছে।ওরাতো মায়ের পেটে থেকে হয় নাই পতিতা গো গুয়া দিয়া অগো জন্ম।,1,crime
ক্ষমতার অপব্যবহার করে আরো কত না কিছু করেছে তদন্ত করা হোক এইসব কুলাঙ্গারে জন্য আজ অনেক বদনাম হয়ে যাচ্ছে,1,crime
জুতা মার সালা গালে।,1,crime
নয়ন বন্ডকে যেবাবে গুলি করে মেরেছে পুলিশ সব কয়টাকে গুলি করে মারার দরকার পুলিশের কাছে একটাই অনুরোধ একটাও জানোয়ারের বাচ্চা যেন না বাচতে পারে এই দুনিয়ার মাটিতে কত নিষ্টুর বাবে কুপিয়ে হত্যা করলো ছেলেটাকে খুবি কষ্ট লাগলো দেখে,1,crime
সালায় কালপিট। মদ খাওরার মতো কথা কইতাছে।ওর নুনু কেটে দেওয়া হক,1,crime
আমি মালায়েশিয়া থেকে বলছি। মিন্নির মতো মেয়েকে ফাঁসির আগে জন ইয়ুজ করার পর ওর সরিলটা টুকরো টুকরো করে কুকুর দিয়ে খাওয়াক। আর ধন্যবাদ পুলিশকে এই যন্ন জে মিন্নির মতো মাগিকে ধরার যন্য। আর ওর গুদির ভিতড গরম ডিম আর আসুলা বাশ দিলে সব শিকার করবো। আমার সোনার বাংলা আমি তোমায় ভালোবাসি। জয় বাংলা জয় বাংলার পুলিশ সেলুট,1,crime
তোদের সব কটার পাছা দিয়ে আইক্কালা বাঁশ দেয়া দরকার খেয়ে দেয়ে আর কোন কাজ নাই?,1,crime
ডিজিটাল বাংলাদেশ এগিয়ে যাচ্ছে চোদাচুদিতে,1,crime
মিন্নি কুত্তারে এখনো কেনো রিমাইন্ডে নেওয়া হয় না এটাই আসল খুনি,1,crime
লুইচ্চা,1,crime
ঐ মাগীরে কি করছে,1,crime
মার হালাগোরে যানে জুয়ার যায়গা আবার ভাত খাইতে আসে ভাত খাওনের আর যায়গা পায়না যারা নিরঅপরাধ তাদের ছেড়ে দেন স্যার সিসি ক্যামেরা দেখেন কে কি জন্য এসেছে অপরাধিদের শাস্তির আওতাই নিয়ে যান,1,crime
সালারে জুতা মারেন,1,crime
সালায় কয় কি কোন দোশ বলে নাই,1,crime
তোর ঘরে মা বোন নাই একদিন তোর মেয়ের সাথে এরকম হবে তখন বুঝবি লুচ্চা কোথাকার।এদেরকে ধরে ফাসি দেয়া উচিত।মনুষের সামনে মুখ দেখায় কিভাবে,1,crime
এরা এত কষ্ট করে এই সরকারকে ক্ষমতায় এনেছে। বিনিময়ে একটু আধটু লূচ্চামিও করতে পারবে না! আর ভাল্লাগে না।,1,crime
এর তদন্ত করবে সরকার এরা ত সরকারের পা চাটা গুলাম তাই এরা অপরাদ করলে সরকার তার তদন্তের দায়িত্ব নিবে। এরা সরকারের কু করমের ফসল। সাবাস বাংলাদেশ বাংগা দেশ ছি ছি ছি থু থু থু সরকারের পা চাটা গুলাম।,1,crime
মাদারচুদের তাও লজ্জা শরম নাই সে বলে তদন্ত চুদাবে।,1,crime
হালারে জুতা পিটা করা উচিৎ,1,crime
মিন্নি খানকির হাত আছে সবার আগে ভিডিওটা দেখলে একটা বাচ্চাও বুঝতে পারবে অথচ পুলিশরা কিছুই বোঝে না আহারে নাবাল্যক পুলিশ,1,crime
জুতার বারি সালা লুচ্চামি চুদাও হ্যাকার দোষ দেও ওর ফাসি চাই না হলে অন্য এসপি ডিসিদের কোনো দামি থাকবে না,1,crime
সালাকে জুতা মারা হোক,1,crime
এই মেয়েটা একটা খাংকি মাগী ওর হাত রয়েছে।,1,crime
এই কুলাংগার এর বাচ্চা কে লিঙ্গ কাটা হোক,1,crime
আচুদার ঘরের আচুদা তোদের মতো আচুদা এখনো বাংলাদেশে আছে বোকাচুদার বাচ্চারা আমার বালের ভিডিও বানাইছস,1,crime
এই শালার কি বিচার হবেনা,1,crime
খাংকি মাগী তোদের আবার সম্যসা কি,1,crime
তদন্ত সে করবে মাগীর পুত,1,crime
হায় রে মানুষ দিনে দুপুরে পাব্লিক প্লেসে একটা মানুষকে কুপানো হচ্ছে আর বাকি সবাই দেখছে সবাই মিলে এগিয়ে আসলে কি করতে পারত ঐ কুত্তার বাচ্চা😠,1,crime
এসব কাদের ফাদেরের কথা আর শুনতে চাই না । এদেরকে যদি পারো হাত পা কেটে দাও। ল্যাংটা করে পাছায় আলকাতরা লাগাও কালা কুত্তার ঘু খাওয়াও। হোগা দিয়ে বাঁশের কঞ্চি ঢুকাও।,1,crime
মাহী চুদা দেওয়া সময় মান সম্যানের কথা মনে ছিলো না আর তর মতো নষ্টা মাগীর হিজাব মানায় না,1,crime
গোয়ামার সেষ কোন সালায় বলে দেশ ডিজিটাল সে সালার গোয়া মার,1,crime
এটাতো পুরাই সিনামার স্টাইলে হত্যা করা হয়েছে কুত্তার বাচ্ছাদের সব কয়টাকে ফাসি দেওয়া হোক,1,crime
ভিডিও দেখে বুঝা গেলো মিন্ন এর সাথে জরিতো আছে। ওর স্বামী কে জোর করে ধরে নিয়ে যাচ্ছে ওর সামনে দিয়া কিন্তু ও কোনো প্রতিবাদ করেনি যখন কোপানো শুরু করছে তখন একটু অভিনয় করলো বাচানোর।আরে মাগি যখন তোর সামনে দিয়া ধরে নিয়ে গেলো তখন চ্যাচা মেচি করলিনা কেন মানুষ ডাকলিনা কেন!!!তুইতো একটা খানকি তোর জন্য আজ দূটি ছেলের প্রান গেলো,1,crime
সালারা তোদের দেশের লোক বাইরের সব দেশেই আছে তোদের দেশের প্রধান এবং পুলিশরা কি জানেনা কেচিনতে জারা যায় তারা অপরাধি নয় শুধু সাধারণ মানুষকে বিপদে ফেলে কি ভাবে টাকা নিবে এই ধানধা,1,crime
মাগী চুদাচুদির সময় মনে ছিলনা। তোর ভুদায় রড গরম করে ছয়েক দিতে হবে।,1,crime
চুদাচুদির কথা হুনতে হুনতে আর ভাল্লাগে না,1,crime
মাগি সোব জানে,1,crime
সারের কোন দোষ নাই আলু নটিমাগি তাইলে দোষটা কার তুই আর তোর সারে তো করছো,1,crime
ও এস ডি ও এস ডি মারাও হগ্গলে বাল ডা মানে কি সেইডা কও না ক্যা,1,crime
তালি এক হাতে বাজেনা ডিসির বৌ ডিসিকে চুদতে দেয়না এটা বড় কারন। একজন পুরুষ মানুষ না চুদতে পারলেই এই আকাম করে। অনেকে আমাকে অসভ্য বলতে পারে কিন্তু আমি খাটি বাংলা ভাষায় কথা বলছি। দেশে সেই রকম ভালো মানের পতিতালয় নেই পুরুষরা একজন আরেকজনকে পুটকিমারা ছাড়া কিভাবে যৌনতা মেটাবে আমার জানা নেই। যে বিষয়টা বলার জন্যে আমি কমেন্ট লিখতে চেয়েছি। সেটা হলো মেয়েটি একটা বেশ্যা এতে সন্দেহ নাই। কথায় আছে যেদিন থেকে নারী বাইরে পা দেয় সেদিন থেকে খানকির খাতায় নাম লেখায়। মেয়েটা বার বার কেমেরার দিকে তাকাচ্ছে লক্ষ করলে বুঝা যাবে। এটা একটা ফাঁদ ডিসিকে বিপদে ফেলার একটা সাজানো খেলা।,1,crime
কুত্তার বাচ্চা ডিসি নামের কুত্তার বাচ্চা এগুলারে সাতরাস্তার মোড়ে ফাঁসি চাই,1,crime
এই ডিসির বৌয়ে মাগী বাজি করে,1,crime
এদের আর কি হবে জত মাদার চুদ,1,crime
এসব খারাপ মেয়েদের ফাঁশি দিয়ে মারা দরকার খানকির বেটি কোতাকার জানি,1,crime
হালা হাসে হালারে জুতা মার,1,crime
প্লিজ এই সব মাগিদের সাখাত নিয়ে নিউজ মিডিয়া কে কলংকিত করবেনা,1,crime
কুক্তার বাচ্চারা মজা করতে ভালোই লাগে তদের 😭😭😭,1,crime
পুলিশ কি বাল ফালাই নাকি গাঞ্জা খায় আবুলের মতো কথা বলে কেনো??? বাংলাদেশের বর্তমান শাষন ব্যবস্থা কিরকম জানি তাই ওই অভিজ্ঞতা থেকে বলছি এখানে কারো ফাসি হবে না বরং দুয়েক মাস যাবে কোর্ট্র নিয়ে যাবে খবরে দেখাবে রায় দিবে এই সেই হাবি জাবি করতে করতে মামলা শেষ বাংলাদেশ এর সব লুট হয়ে গেছে,1,crime
জারজ লীগ,1,crime
জুতা মারো মাদারচোদ ডিসির বাচ্চাকে শালা শুয়োরের বাচ্চা,1,crime
এই হালারে ধরে ওর ধন কেটে দিওয়া হওক,1,crime
লোকটার কোন লাজ লজ্জা নেই বেহায়া বেশরম কোথাকার 🙈🙈🙈🙈🙈🙈,1,crime
কতকিছু ঠিক থাকার পর ও অস্বীকার করে বাইনচুদ,1,crime
মিন্নি কানকি ক দুরে নিয়া জাক ওকে পুলিস রিমান্ত দিলে কইবো,1,crime
ভাই এখানে যারা কমেন্টস করেছেন সবার টাই ভালো তবে আমি যা লিখবো সেটা আমার মোনের রাগটা প্রকাশ করতে চাই ওই ডিসির বৌ কে চুদবে সবাই ডিসি বোসে বোসে দেখবে যে ভাবে ও চুদেছে আর ওর ধোন পাথরের উপরে থুয়ে হাতুর দিয়ে ধোনের আগায় বাড়ি দিতে হবে আর ওই মহিলার ভোদায় ঘোড়ার ধোন ঢুকাতে হবে মাগি স্বামি থুয়ে পরের সাথে চুদা লাগাও মাগি,1,crime
আস্তো একটা মাদারচোত,1,crime
মাগি মিথ্যা বলে বুদার মাঝে তৈল ডেলে আগুন দেয়া দরকার,1,crime
মাদারিকে জুতাপিটা করলে বেইর হবে,1,crime
কুত্তার বাচ্চাদেরকে এতদিন বাঁচিয়ে রাখা উচিত ছিল না। ধূর্ত ফাঁসি কার্যকর হোক,1,crime
যে হালা বলচে যে এটা সাজানো ঘটনা এই শালা ও অপরাধির চেয়ে ও বড় হারামি কেলেব!!!!!!,1,crime
চুতমারানি,1,crime
এই শালার পুত তুই কান্না কর কেন,1,crime
কুত্তা লীগ থাকা কালিন দেশে কোন সঠিক বিচার হবে না।,1,crime
সাব্বাস কাকের কণ্ঠে কুকিলের সুর হারামির বাচ্চা,1,crime
আবাল মার্কা দেশে বাস করি আমরা যেদেশে আসামীই তার মামলার তদন্ত করে,1,crime
এই মাগির সেক্স আছে বহু,1,crime
সালা সালির জুতা মারো,1,crime
মিনি জড়িত মাগির ফাঁসি দেওয়া হোক,1,crime
লুচ্চা মেয়েরা লাইন ধরুন,1,crime
এতগুলো মানুষের সামনে একটা মানুষকে মেরে ফেললো হিজরা রাও তদের থেকে ভালো আছে,1,crime
ও সব জানুয়াররা মিন্নিকে পাওয়ার আশায় রিফাতকে খুন করল।কিন্তুু ছলনা করছে মিন্নি তাহলে রিফাতকে কেন মারলি।মিন্নির কে নিয়ে সবাই সাদ মিটাতি তাহলে এর সঠিক বিচার হত।,1,crime
এই মাগিরে কুপানোর দরকার আর এই মাদার চোদ অকলরে কুপানো ও দরকার,1,crime
কুত্তালীগ এর জানোয়ার দের কাছ থেকে এর চেয়ে বেশী আর কি আশা করা যায়,1,crime
সরকারী মাল বইল্যা কথা ভাই।,1,crime
খানকির বাচ্চা হইবো তাই মাথা ঘুরায় 😂😂 ডিসির কনডম ফুটা ছিলো 😂,1,crime
ডিসিচোদাঠিকআছে,1,crime
রিফাতকে যখন ধরে নিয়ে গেলো তখন মিন্নি সাম্ভাবিকভাবে নয়নের দলের সাথে হেটে গেলো এটা দেখেই বোঝা যায় যে মিন্নি মাগী পুরা জরিত,1,crime
তোদের মারে চুদি খানকির পোলা তোরা জারজ সন্তান,1,crime
পাগল চোদা,1,crime
দেশ টাকে মাদারচোদেরা আগরা বানিয়ে পেলছে।হাম্মালিগ হাম্মালিগ চোদার লিগ?,1,crime
বালের টেলিফ্লিম,1,crime
হালার পুতকে জুতা পিতা কর,1,crime
লুচ্চামি 😡,1,crime
শালা ফকিন্নির পোলা!!!! আবার নাম রাখছে বন্ড 🤭🤭,1,crime
মাগি তোর ভুদা দিয়া হিমালয় ঢুকানো উচিৎ,1,crime
নুসরাতের পরিবারের সাথে আমরা ও কেঁদেছি। এখন তোমাদের পালা। কুলাংগারগুলা আকামটা করতে একবার আপনাদের কথাতো মনে রাখেনি।,1,crime
এই খানকির পুলাদের ব্রাশফায়ার করা হোক।।,1,crime
স্যারও মজা পাইছে আমিও মজা পাইছি তাই স্যারের কোন দোষ নেই। এই মহিলা আবার বিচার চাচ্ছে বাচ্চার দোহায় দিচ্ছে। আরে বেয়াদব বোন এইসব খারাপ কাজ করার সময় আপনার বাচ্চাটার কথা মনে ছিলো না। আপনার মত বোনদের জন্য আজ সমগ্র বোনরা আতঙ্কিত।,1,crime
মাগি ভালোবাসা চুদায়😁😁,1,crime
মিন্নি খানকি মাগিডারে যোনী দিয়া এসিড প্রবেশ করিয়ে রিমান্ড এ জিজ্ঞেস করা দরকার,1,crime
সাংবাদিকরা এখন মুরগির বাল দেখে মুরগার বাল দেখে না!!,1,crime
এই মিথ্যা বাদি মাগি তুই যদি চেষ্টা করলে পারতি তোর রিফাতকে বাচাতে তোর কোনো কথা আমরা বিশ্বাস করবো না ডায়নী,1,crime
চোরের দশদিন গেরস্তের একদিনে যথেষ্ট এই দুই লুচ্চা লুচুন্নিদেরকে আইনের আওতায় এনে উপযুক্ত সাস্তি দেন এদের কারনে সমাজ নষ্ট হতেছে,1,crime
যে লোকটা এই ভিডিও টা শেয়ার করছে তাকে অনেক অনেক ধন্যবাদ এই ধরনের মুখোশ ধারী লুচচারা কখনো দেশের জন্য কিছু করতে পারে না শুধু লুচচামিই করে শালা চরিত্র হিন ওরে জুতা পিটা কর আগে,1,crime
ভাই সানজিদা ইয়াসমিন সাধনা কে জামালপুর পতিতালয়ে পাঠিয়ে দেওয়া হোক জন সাধারনের কাজে লাগবে এছাড়া ডিসি আহম্মদ কবিরকে পতিতালয়ের দালাল বানিয়ে দেওয়া হোক,1,crime
বড়্গুনার হত্যা যারা দাড়িয়ে প্রত্যক্ষ করেছে সাহায্য করাতো দূরে থাক তারা হচ্ছে নপুংসক । এর বেশি আর কিছু বলতে চাই না। আর মিন্নি হলো নারীজাতির কলংক,1,crime
হায়রে মাদারচো যে ক্যামেরা লাগিয়ছে তাকে পুরস্কার দেওয়া উচিৎ,1,crime
বালের ভিডিও বানাইছো প্রোতিবাদ করো,1,crime
সালার আবাল তোর লজ্জা সরম নাই আবার বলে ঘটনা টি খতিয়ে দেখবে।,1,crime
সালা লুচ্চামি কইরা ধরা পড়ছে আর বলতেছে যে তাকে ফাসানো হইছে সালা লুচ্চা কুত্তার বাচ্চা লজ্জা করেনা বুড়ো বয়সে লুচ্চামি কইরা ধরা পড়ছে লুচ্চা টাকে চাকরি থেকে বরখাস্ত করা হোক।,1,crime
অাগে মাগীর বিচার হোক,1,crime
খেলা দিয়ে পরে চলে গেছে বাংলাদের চুদানির পুতাই এখন কোথায় তরা জদি একটা মোতুয়ায় এস করতো তাহলে আনলোন করতে তরা এখন কর তার ফাসি চা কারন এরা আমাদের দেশটা নষ্ট করে দিছে,1,crime
ঘটনা সত্য।তাকে প্রকাশ্য জুতা দিয়ে পিটানো হোক।।সালা লুইচ্ছা।,1,crime
সব শালারে পোন্দে সিদ্ধ ডিম আর গরম রড দেওয়া উচিৎ।,1,crime
কথায় আছে কয়লা দুইলে ময়লা জায়না। এতো সুন্দর বউ থাকতে আরেক মেয়ের সাতে হছটি নছটি করে। শালায় আসলে একটা খারাপ,1,crime
শালি তোর জন্য ছেলে টা জীবন গেছে শালি নয়ন কে বিয়ে করছে মাগী সব অভিনয় করছে,1,crime
সিসি ক্যামেরায় সে নিজে ওসব ধারন করে ব্লাকমেইল করে আসছিল। কথায় আছে চোরের দশ দিন গেরস্থের একদিন। পাপ বাপকেও ছাড়ে না। কুত্তার বাচ্চাদের জুতা পেটা করা উচিত।,1,crime
মাগীর জামাই এখন কই জামাই কি কয় সুনতে মন চায়,1,crime
তুমি মরে যাও তুমি এদেশে বাঁচার অধিকার নাই তোমার মতমাগী এদেশে বাঁচার অধিকার নাই এগুলা করার আগে তোমার সন্তানকে কথা মনে ছিল না,1,crime
মাগির ফুলা করছে কামটা,1,crime
সালার এমনই হতে পারলাম না,1,crime
তুই একটা মগির বড় দালাল,1,crime
আর কিছু আবাল আছে মিন্নিরে বিয়া করার জন্য পাগল আছে। এই মেয়ে কত খারাপ ভিডিওতে দেখেন।,1,crime
দুর মাদার চোদ হগল এটাকি,1,crime
এই মাগীর সোনাটার মধ্যে কচু ডুকা এই মাগী কাজটা করেছে,1,crime
এ সব যারা করে তাদেরকে বহিস্কার করা উচিত। হারামজাদা বদমাশ। ওরা সরকারের পালিত জানোয়ার। আর এদের উপর ভরসা করে ভোট চোর সরকার ক্ষমতায়।,1,crime
কিসের তদন্ত এই লুচ্চা হারামি চুতমারানি কে আজই বহিস্কার করে চুদাবাজির দায়ে গ্রেফতার করা হোক,1,crime
মাগি তরে কি ধর্ষন করছে সেচ্ছায় তো খাউজ মিটাইতে গেছিলে। তোদের মত বেশ্যা মাগিদের কারনে দেশে এই অবস্তা,1,crime
এই মাগির পুটকির ভিতরে পদ্মাশেতুর পিলার ঢুকিয়ে দেয়া দরকার মাগি চোদা দেয়ার সময় মনে ছিল না। 👹😈😈,1,crime
হায়রে মানুষ তোদের কুওা দিয়ে চোদা দরকার,1,crime
শুয়োরের বাচ্চা এখন কেঁদে লাভ নেই কারণ অন্যায় করার আগে ভাবা উচিৎ ছিল এখন শুধু ফাঁসির দড়িতে ঝোলার অপেক্ষায় থাক ।,1,crime
হালার লুচ্চা ডিসি,1,crime
এই খুনে মাগীটার হাত আছে এটা বুঝা যায়,1,crime
কুত্তার বাচ্ছাইন সুন্দর লাগে তদের,1,crime
হালার পুতেরা মিন্নি খানকির দালাল,1,crime
এই বদমাইশ লুচ্চা ডিসির পদক কেড়ে নিয়ে যে ভিডিও টি আপলোড দিয়েছে তাকে দেয়া হউক।,1,crime
ডিসির মারে চুদি মাগির পুতরে দেয় হাচিনা,1,crime
মাদার চুদ তরে চিরা জুতা দি কালি পিটাইতো আচিলো কান কির পুলা তর পাশে জে মালটা আচে ওটা তো করতে পারতে না,1,crime
অাহারে মাগি,1,crime
জারজ দের অতি দ্রুত ফাঁসি কার্যকর করা হ‌উক।,1,crime
সালারা চোর,1,crime
শালাকে কবিরাজ দেখা দরকার ।,1,crime
তারে জুতা দিয়ে পিঠায়া চাকরি থেকে বরখাস্ত করার দাবি।,1,crime
দুর মিয়া এ তো আগের কাহিনি আসল রহস্য কি হল সালা সবি চাপাবাজ,1,crime
সালা বুড়া পাডা।,1,crime
ঐ ডিসি মনে হয় আগে যোনলীগের সধ্যস্যো ছিলো না হয় এমুন পদে থেকে এ গানিত কাজ করতে পারেনা,1,crime
আর ডিসি হল খানকির পোলা লুচ্চা,1,crime
বাহ শালারপু,1,crime
এইগুলি তো আওয়ামী লীগে কুত্তা লীগ।।,1,crime
সেক্সী ডিসি,1,crime
এতোগুলো মানুষ দাড়িয়ে দেখলো কেউ এগিয়ে যায় নাই এগুলো সব অমানুষের বাচ্চা,1,crime
মাগীর ভোদাটার মধ্যে ডিম দিয়ে দেখা উচিত ডিমটা সেদ্ধ হয় কি না!বেষ্যা মাগী আবার মিডিয়ার সামনে এসে বলে ওর বাপের দোষ না।।।দোষ হবে কেমনে তুই তো নিজ ইচ্ছাই ভোদাটা খুলে দিসছ।।।।,1,crime
এখন এই বাল ছাল নিয়েই পরে থকো,1,crime
পুলিশকুত্তা গোলো গরিবের বালো চায়না তারা টাকা খেয়ে বড় বড় সমসা গোলো মাটি চাপা দেয় তাই খারাপ পুলিশ গোলোর পোসাক খুলে মারতে মারতে পিসিয়ে ফেলা দরকার,1,crime
এই জানুয়ার টাকে চিডারের বাচ্চার ধন কেটে যাবত জীবন কারাদণ্ড দেয়া হোক্ প্রশাসনের কাছে বিচার চাই যাতে করে পশু গুলো সাবধান হয়ে যায়,1,crime
অরে বাবা!! কিরে খানকি মাগি! তুই বোরকা কেন পরে আছিস চুতমারানি তরে পেনটি পরায়া রাস্তায় নামানো দরকার।চুতমারানি বোরকার অপমান করিস,1,crime
ওই বেশ্যাটাকে জন সম্নুখে আনা হোক,1,crime
তুই মরে জা তোরা বেচে কিহবে মাগির জাত,1,crime
কুত্তার বাচ্চা ঐ মেয়ে কে রিমান্ডে নিলেই সব রহস্য বের হয়ে যাবে,1,crime
আরে ছাগলের বাচ্ছা মাদ্রাসা কোনটা তাও জানিস?,1,crime
খানকি তরে পাইলে চুদা কারে কয় বুজাইতাম। আমিও বলি স্যারের কোনো দোষ নাই সব দোষ তর। তদের মত এমন ব্যাসসার জন্য আজ বাংলার ঘরে ঘরে অশান্তি।,1,crime
সালা ঠিক মত ঠেলতে পারে না মিনিট পর মাল আউট হয়ে গেলো 😁 🤣🤣🤣🤣😂😅😂😅😂😅😂,1,crime
মাগির ফাঁসা চাই,1,crime
মাগী সেই নাটকবাজ। ওর নাটক দেখে ওরে কোপাইতে ইচ্ছা করতেছে। ও এই হত্যার সাথে জড়িত।,1,crime
শুধু দেখানোর কি দরকার এই জানোয়ার দের খুব শীঘ্রই ফাঁসি দিতে হবে ?,1,crime
সালা লুচ্চা সালাকে ফাঁসি চাই,1,crime
বেশির ভাগ পুলিশ মাদার চোদ,1,crime
ফাসি দিতে দেরী হলে সবাই প্রসাশণ ও সরকারের গোসঠী চোদেন।,1,crime
তদন্ত তদন্তে ই দিন যাবে দেশটাকে জাহান্নাম বানিয়ে দিলো কুত্তারবাচ্চারা,1,crime
মার সিন্নি ডিসির তাউল্লায় ডিসিকে কলিকাতার হারবাল খায়াও,1,crime
এইগুলো হলো পতিতা মাগি বেশ্যা খানকি চোদাচুদির তদন্ত করতে চায় খুব মজা পাইছোস না মাগি মজা তুই ও পাইছোস মজা তর স্যার ও পাইছে,1,crime
কেমেরা যে লাগিয়েছে তারে পুরুষ্কার দেওয়া হোক। আর এই ধরণের উচ্চ পদস্থ কর্মকর্তাদের রোমের সামনে পতিতালয়ের নারী রাখা হোক তাদের মন চাইলে সিবলিস গনরিয়া এইডস তৈরী করুক। তবু দেশ নিরাপদে চলুক।,1,crime
ফাঁসি না হইতেই হয়ে গেল বোকাচোদা ভুয়া খবর,1,crime
এই নডি ডিসির চোদা খেয়ে বিয়ে করার চাল করছে।,1,crime
বাংলাদেশে কুকুরের মত কাজ কাম চলতেছে এক জন বড় মাফের মানুষ হয়ে অপিসে এই রকম নিচু কাজ কি ভাবে করে সালা কে জুতার বারি দিলে ঠিক হয়ে যাবে,1,crime
সেরকম হয়েছে ডিসি সাব বাংলাদেশের নতুন পর্ন স্টার !! !!,1,crime
হালার ঘরের হালারা বাল করছে,1,crime
বাল বানাইছে এরা তো মিন্নির পক্ষে কাজ করছে,1,crime
মুক্তিযুদ্ধের চেতনা বিক্রি করে । জুয়ার আসর বসিয়ে চাপা মেরে চেতনা চেতনা চোদায় । খানকির পোলারা মুক্তিযুদ্ধারা কি কখনো বলেছিল চেতনা বিক্রি করে খা ? কুত্তা লীগের বাচ্চারা দেশটারে দুইটা ভাগে বিভক্ত করে দিয়েছে আর বলে আমরা মুক্তিযুদ্ধের পক্ষের লোক । বাকি এই দেশের লোক গুলো কি এই দেশে ভেসে এসেছে নাকি রে ? কুত্তার বাচ্চা রা ।মাদারির বাচ্চারা এই জিনিস টা বোঝে না । প্রত্যেকটি ক্রিয়ার একটা বিক্রিয়া আছে । শালা চাটুকারের দল ।,1,crime
শালারা তখন মনে ছিলনা,1,crime
তোগ বাব দাদা সোনা,1,crime
কুত্তার নজর গুয়ের দিকে,1,crime
অই সালার বিচি কাইটা দেয়া হক,1,crime
শয়তান মহিলা চোদার খাইস মিঠেনাই কেউ পারলে আবার চুদি দেন,1,crime
শালা তরা এই সব ব্যপার নিয়াও মজা করছ। শালা মাদারচুদ,1,crime
এ কেমন বিচার চুদা দিয়া বিচার চায় হায় রে পতিতা তোর আগ্রহ টাই বেসি ছিল,1,crime
বালের তদন্ত আর বালের রিপোর্ট এই সাউয়া গুলো খেয়ে নিবে সার্টিফিক্ট প্রাপ্ত সন্ত্রাস পুলিশ 😂😂😂,1,crime
আশ্চর্য এইটা নিতান্তই তাঁর ব্যক্তিগত ব্যাপার শুধু শুধু অশিক্ষিত সাংবাদিকগুলা তারে এম্ব্যারাস করসে তাঁর খাড়াইসে ওই বেটি তারে আরাম দিসে যা হইসে তা তো আপোষেই হইসে আজব!,1,crime
কিসের তদন্ত ওই মহিলা কি মা হতে যাচ্ছে কিনা বালের আইন কানুন 😬,1,crime
শালার বাচ্চা গাঞ্জা খোরের মত কথা বলছে জুতাপেটা করা উচিত এসব কুত্তালীগের চামচাদের,1,crime
এই খানকির পোলারে আইন এর আওয়াতা আনা হোক আর তার চাকরি বাতিল করা হোক,1,crime
জুতা মার খানকির পুলা রে,1,crime
ওহমমম সাংবাদিক ভাইয়েরা নিউজ চুদাইয়া উল্টাই দিছ। সালা বালপাকনা চুদারা সামাজিক মাধ্যমে আসার আগ পর্যন্ত কোন বাল ফালাইতেছিলা। এহন এই হবে সেই হবে। শুয়োরের বাচ্চা খানকির পোলারা একটা ইস্যু পাইলেই হইছে।,1,crime
ভাত খাইতে আইছে সালা,1,crime
মিন্নি খাটো মাগি মাগির মারে চুদি মাগি আস্তে হাটে আবার মাগি কে নয়ন মাদার চোদ কিছু করেনি। মাগি জডিত,1,crime
নুনু কেটে দে,1,crime
হালার পুতেগো গু খাওয়ে মারা দরকার,1,crime
মাইংকা ডিছি ছিরে লেংটা করে মথায় কামায়া কিছু দিয়ে গলায় জুতার এই সেই পরিয়ে তার অফিসে হীরনসি লাগিয়ে পুটকি মারাবার দরকার,1,crime
মাদারচোদ রা তোদের কি কাজ কাম নেই,1,crime
মাগি একটা বেসসা,1,crime
তুমারে কে চাকরি দিছে মাগি,1,crime
ইস্ কী চোদনটাই না চুদছে ধরে । অসুস্থ তো হবার কথাই 💝 । নিষ্ঠুর ডিসি মহিলার ছবি প্রকাশের জন্য আমি নিন্দা জানাচ্ছি আছে ভোদা দিসে চোদা । যে চুদছে তার ভিডিও কৈ । নাকি ঐ ডিসি তোমার পুটকি চুদেছিল তাই ভিডিও দাওনি,1,crime
চুদা চুদি করার সময় ছেলে মেয়ের কথা মনে পড়ে না ভাল সারা জিবন না অন্যর বিডিও দেখচে আর এখন ৃ না নিজের মার সেক্স দেখবে,1,crime
একটা সুন্দর জীবন মূহূর্তে শেষ করে দিল জানোয়ার গোলা। তখন কই ছিল এই কান্না,1,crime
একটা জিনিস বুঝতেছি না মিন্নি মাগিকে কেন গ্রেপ্তার করা হচ্ছেনা। নং আসামি মিন্নি কিছু অংশ বাদ দিয়ে ভিডিও দিছেন। মি্ন্নিকে সেভ করতে চয় সবাই। ন্যায়বিচার হবেই মিন্নিকে গণচোদা চুদতেই হবেই,1,crime
চোদাবার প্রকাশ্যে ফাঁসি দেয়া মৃত্যুদণ্ড দেওয়া হোক,1,crime
কুলাঙ্গার সন্তানেরা নিজেদের মা বাবাদের কথাও ভাবলোনা এমন জঘন্য কাজ করার আগে। আর এতো জঘন্য কাজ করেছে যে সন্তান তার জন্য কান্না আসে কিভাবে?,1,crime
বাচতে চাস চুদার সময় মনে ছিলো না বাসায় সন্তান আছে,1,crime
আবার গান গাইতে ও ইচ্ছে করে ধুর পাগলা চরিএহীন লম্পট অসভ্য ফালতু অপদার্থ নষ্ট জঘন্য অপরাধি।,1,crime
মাগি মহিলা,1,crime
একটা মানুষ মানে মিথ্যা কথা কিভাবে বলতে চোখের সামনে সবাই দেখলো তার পুরো মিথ্যা কথা বলতেছে বাটপারের বাচ্চা আর আপনারা বলদ নাকি আপনারা এইগুলা তদন্ত করার কি আছে এই ভিডিওকে অসত্য প্রমাণ কোন শালায় করতে পারবে,1,crime
এই খানকির মেয়ে সহ । মামলার সকল আসামিকে নয়ন বন্ডের মতো অবস্তা করা দরকার। তাহলে দেশবাসি সস্তির বাতাশ পেতো। কারন এই মাগি নষ্টের মুল।,1,crime
মাগির পোলা কি কশ,1,crime
হায় রে মায়ের জাত বুকে মারিস লাথ মুখে তুলে ভাত ডাইনিতে আর তোর মাঝে আছে কি তফাত। এ জাতি বড় খাটি কখনো পাক কখনো নাপাক পতিতালয়ের মাটি,1,crime
অবৈধ সরকারকে হঠাও সব ঠিক হয়ে যাবে।সালারা নামও রাখছে মুক্তিযোদ্ধা ক্লাব। সাংবাদিকদের কাজ হচ্ছে কোথায় কি হচ্ছে তা তুলে দরা ত আগে কি বাল ছিরছো তোমরা এখন বড় বড় কথা বলছ এতোদিন সবার সামনেই এই খেলা চলছে এবং প্রশাসন সহ অন্যরা ও কমিশন ও খাইছে প্রধানমন্ত্রীর বলার পর সব সালারা ভালোর নাটক করতেছে বেশীরভাগই বাটপার সরকার আমাগের পাগল পাইছে সরকার জিরো টলারেন্স ঘোষণা দিয়ে বিরোধী দলের ব্যাবসায়ীদের তাড়িয়ে দিয়ে নিজেরাই একচেটিয়া ব্যাবসা করে যাচ্ছে।,1,crime
এই কুত্তার বচ্চারা এই ঘটনাকে কেন্দ্র করে ব্যাবসা শুরু করতেছে।এইসব কুত্তাদের ধীক্কার জানাই থু থু দেই এসব লোকের,1,crime
বালের নাটক,1,crime
ঐ বেটা সাংবাদিক শাক দিয়ে মাছ ঢাকার চেষ্টা করিস না । সবাই ভিডিও ফুটেজ দেখেছে শুধু তুই ছাডা । কত টাকা পেয়েছিস শালা বাটপার ।,1,crime
সব সালাদের গুদে গরম রড ঢুকালে আসল খবর বেরুবে।,1,crime
আকাম করণ টা করছে । এখন ভালো সাজতে ছে মাগি । বাচাঁর জন্য সন্তানের কথা বলতেছে । যখন করছে তখন মনে ছিল না। দুই জনের দোষঁ । স্যারের থেকে টাকা খেয়ে এখন স্যারকে ভালো বলতেছে । এদের জন্য দেশের আজ এই অবস্হা । দুই জনের পাশি চাই । যাতে করে কেউ এই ধরনের কাজ করতে সাহস না হয় । ধরা খাইচো মামু । অবার ডেলা সামলা ।,1,crime
লুচ্চা কমেডি সেক্রেটারি এতে কোন ক্ষতি ক্ষতি হয় শালার ঘরের শালারা,1,crime
ভাই অভিনয় কিছু টা ঠিক আছে কিন্তু মিন্নির খাংকির কিছু মিল নাই,1,crime
সালিকে ফাঁসি দেওয়া হক,1,crime
ঔ মাগির ফাসি চাই,1,crime
বালের বাংলাদেশ,1,crime
মাগির পোোলারা সব জানোয়ার,1,crime
কোন চুদির পোত ভালো না সব সালার আড়ালেই লুকিয়ে আছে একটা না একটা,1,crime
মাদার চুদ তর বনেরে ডিসি চুদবে দিবি নাকি ডিসি কাছে দালাল খানকি পুলা,1,crime
মাগি👌👌🖕🖕,1,crime
ওখানের সবাই বোবা আর লুলা ছিল তাই কিছু করতে পারেনি। আর মিন্নি জাহান্নামে ও ঠাই পাবেনা।আর মিন্নির মত লুচ্চা এবং জগন্য মেয়ে দুনিয়াতে নেই। মিন্নির বিচার দুনিয়াতে নাও হতে পারে ওর বিচার আল্লাহ করবেন।কারন সবার বদদোয়া ওর উপর রয়েছে।এখন ওর বেচে থাকার থেকে মরে জাওয়া অনেক ভাল।,1,crime
জুতা দিয়া পিটানো উচিৎ সালা ডিসিকে চাকরি থেকে অব্যাহতি দেয়া হোক।,1,crime
এই খাংকির এটা পরি কল্পিত কাজ!!!!,1,crime
কুত্তার বাচ্চা নয়ন তোরে যেন আল্লাহ মাফ না করে। তোর উপর আমার বদ দোয়া রইল।,1,crime
এটাই বাংলাদেশ যেখানে প্রকাশ্যে খুন হয় অতচ মানুষ দাঁড়িয়ে থেকে দেখে এর পর যখন একজন নিহত হয়ে যায় তখন ফেইসবুকে শোক পালন করার মতো মানুষের অভাব হয়না ইউটিউবে নানা রকম ভিডিও আপলোড হয় ।অতচ সেদিন যদি এই মানুষ গুলো সেখানে হিজড়াদের মতো দাঁড়িয়ে না থেকে প্রতিবাদ করত তাহলে একটা তাজা প্রাণ ঝরতনা ।,1,crime
কিশের ডিসি সালাই মাদার চুদ,1,crime
পাপ বাপকেউ ছাড়ে না।সালা লুচ্ছা,1,crime
সালার ডিসি তখন মনে হয় নেশা অবস্থায় ছিলো এই জন্য সিসি ক্যামেরা দেখে নাই,1,crime
এরা বিয়ে করবেনা আর প্রথম শ্রেণীর কর্মচারীদের সাথে বিছানায় যাবে তাতে কোন সমস্যা নেই যে সমস্ত কর্মজীবী মেয়েরা বিয়ে করেনা অথবা ডিভোর্স হওয়ার পর বিয়ে করেনা তাদের বেশিরভাগই এরকম রাষ্ট্রীয় মাগী।,1,crime
বাংলাদেশ শতকরা নারীদের চাকুরী নামে তাদের ইজ্জাত লুট করা হচ্ছে জামালপুর মানুষ বেজম্ম ছোটলোক টাটকা শয়তান,1,crime
এই কুত্তা গুলো কেনো মরে না এই জানুয়ার দের জন্য আরো বেশি ক্ষতি হচ্ছে দেশের বন্ধ কর খানকির পুলারা,1,crime
আরে এই কুত্তার বাচ্চাদের ফাসি দেওয়া দেরী হয় কেন আর এই নাপিত বলে ও জানেনা কেন ফাসি হয়,1,crime
কানখির পোলাকে জুতা মারতে মারতে হত্যা করা হউক,1,crime
খানকি মাগির চুদানোর সময় মজা লাগছিলো তখন বাচার ইচ্ছা ছিলো চুদাইতে গিয়ে দরা খাওয়ার পরে এখন তার বাচার ইচ্ছা নাই,1,crime
তোর মার বুূদা দেখাইলি,1,crime
জামাল পুরের ডিসি লুচ্চা তার দ্বারা দেশের উন্নতি সম্ভব না তাকে চাকুরী থেকে বরখাস্ত করা হোক,1,crime
সালা হাসিনার গুয়াই যা খানকির পুত,1,crime
এই মাগি কে কেনো পাশি দেউয়া হয় না,1,crime
কুকুরের বাচ্চা সব গুলো কে ফাঁশি দাও,1,crime
মিন্নি মাগি তো পিছে পিছে হেটে যাচ্ছে যখন ছেলেটাকে কিল ঘুসি মারতে মারতে নিয়ে যাচ্ছিলো পোলাপান।কই তখন তো সে আটকাতে গেলো না।স্পষ্ট বোঝা যাচ্ছে সব।ওরে এখনো কেনো গ্রেফতার করেনা পুলিশ??সেটাই মাথায় আসে না।,1,crime
এই লুচ্চার ঘটনা খতিয়ে দেখার কিছু নেই আগে জুতো পেটা পরে খুচিযে খুঁচিয়ে দেখা দরকার ।,1,crime
সব ধর্শন কারিদের মাইরা সাফ কইরা ফেল মাদারি রা।,1,crime
চোরের মার বড় গলা শালা এবার ফাইসা গেছে ভালোবেসেছি শালা ধরা খেয়ে গেছে,1,crime
সালিকে জতাপিটা করেন,1,crime
গোটা বাংলাদেশ আজ বেশ্যাপাড়া হয়ে গেছে,1,crime
বাল হবে বাল😠😠,1,crime
শালা একটা লুচ্ছা,1,crime
তোর মারে চুদেচে সে জন্য খানকি পোলা🔊🔊🔊📢📢,1,crime
কুত্তাগুলা সব জায়গা দখল করে আছে,1,crime
তোর মায়েরে চোদি,1,crime
শালীর ছাওয়াল তোমরা চুমা চুমি করলে সেটা ইডেড বলে চালাও আর সাধারণ মানুষ একটা বাই বাতাস দিতে সেটা বড় কিছু বলে চালিয়ে দাও আর ডিসি মুখের কথা শুনে ভালোভাবে বুঝা যাই শালার পুত মিথ্যা বলছে,1,crime
এটারে দেখলেই বুঝা যায় কি পরিমান লুচ্চা।,1,crime
এই নারী নয় পট্টির মাগি,1,crime
শালারে জুতা পিটা করুন,1,crime
ডিসি তোমার ক্ষতি করে নাই তাতো আমরাও দেখছি কিন্তু তোমারে মজাতো দিছে।আমরাও মজা দিমু আসো ডিসির বুড়া ধোনের চেয়ে আমারটা আরো বড় এবং মোটা বেশি মজা পাইবা।,1,crime
ভিডিও দেখলাম সবাই তাও বলছে সাজানো ষড়যন্ত্র বজ্জাত ডিসি ঘরের বউ এখন ডাল ভাত পরের বউ নিয়ে মাখন খাও শালা । মহিলা টাও খারাপ,1,crime
বুরো হারামজাদা সিরাজিকে আগুনে পুরানো হোক। বাকিদের ফাসি,1,crime
লুচ্চায় দেশটা ভরে গেছে।,1,crime
শালার পুতেরে ফাসি দেওয়া দরকার,1,crime
ক্ষমতার চোদায় দরছে তরে তর বউ চোদে আরেক জন গিয়া দেখ সালা,1,crime
মালে কয কি সারের দুষ নাই ত কে চুদল তোমাকে,1,crime
তরে কে কইছে খবর পরতি সালা,1,crime
কুত্তারা নুসরাতকে মারার সময় বুঝতে পারেনি মরার কষ্টটা এখন বেচে থেকেই মরার স্বাধ বুঝতে পারছে।,1,crime
আহারে খানকির পোলা পাপ বাপকেও চাড়ে না,1,crime
সরকারি ক্যাডার লুচ্চো,1,crime
তোর ছারের যে চুদা খাইলি আর তোর স্যারের কোন দোশ নাই বেথা পাশ নাই,1,crime
খাংকির পতরে গুলি করা উচিং,1,crime
মাগি সহ সবার ফাশি হওয়া উচিত,1,crime
আমি না লেখে পারছি না্ মাইয়ার মারে চোদি তাইরে ও চোদি এই খানকি মাগি জরিত তাইর হাটাি বুঝা যাই,1,crime
শালাকে বহিষ্কার করতে পারেনা সরকার,1,crime
কুত্তার বাচ্চা প্রথম আলো মি এর টুকু কাটালি কেন? এইখানে যে মিন্নি বেস্যা খুনিদের অপেক্ষায় ছিলো সেটা দেখালি না কেন? মাদারচোদ রিপোর্টার,1,crime
খানকি মাগির পোলারা তোরা আর কি কি করবি 😑,1,crime
সাধনার পেটে ডিসির বাচছা আছে,1,crime
হালার পুত কিছুই বুজলাম না সুধু তর নাকের টান সুনলাম,1,crime
মেয়েটা অনেক পর্দানশীল। আকাম করার সময় ও সে হিজাব খোলে নাই। ভাবা যায়😉😃,1,crime
ওই মাগী তের রেট কত,1,crime
পাপের ফলতো পেতে হয় কুকুরের বাচ্চা মুখে জুতা মার,1,crime
বিচার হবে কঠিন বিচার সব দোষ ক্যামেরার।। কেন এমন ভিডিও হলো হাসাইলি রে মাগী,1,crime
মাগীর বিচার চাই,1,crime
যত দ্রুত সম্ভব ফাঁসি কার্যকর হোক । এদের মতো নর পিশাচ অত্যাচারী গোটা বিশ্বে বিরল। ফাঁসি তে তো কষ্ট কম। রাফির মতো জানোয়ার গুলো কে কেরোসিন ঢেলে আগুন ধরিয়ে দেয়া দরকার ছিল । এদের মধ্যে কাউকে করুনা বশে ছেড়ে দিলে বাংলা দেশের জনগণের কপালে আরও দুর্ভোগ ঘনাবে। তাই কালতিবিলম্ব না করে ফাঁসি র কাজ শেষ করা হোক । রাফি র জ্বলন্ত আত্মার চিরশান্তি লাভ করুক ।,1,crime
এখন থেকে যে মন্ত্রী মুক্তিযোদ্ধার কথা বলবে তাকে কুত্তারমত পিটানো উচিত।,1,crime
বালের আগা বানাইচত হালার ঘরের হালারা,1,crime
অফিস রুমের পাশে এমন কক্ষ পৃথিবীর কয়টি দেশের আমলা পায়। চুদার জন্য ব্রিটিশরা এসব করেছিল এবং এ ধারা এখনও আছে।,1,crime
মাগির পোলারা মেয়েটার দোষ দেশ কেনো মেয়েটা যদি মারার পেলেন করতো তাহলে তো মেয়েটা নয়নের সাথে পালিয়ে যেতো,1,crime
এই কুলাঙ্গার বেয়াদব হলুদ মিডিয়া গুলো একটা ফালতু,1,crime
জাতী আজ লজ্জিত তোদের মতো মাদারচোদ গো কারনে এই মাদার চোদ তোর দনের কত পাওয়া রে বউর সাথে বড় জুর থাকতে পারছ তোর তো বউ আছে তাহলে আরেক জনের ধুদের দিকে পাছার দিকে নজর পরে কেন সালা কুকুরের বাচ্ছ,1,crime
আমি হলে শালাদের পাছায় বাঁশ ঢুকিয়ে রোদে শুকিয়ে দিতাম,1,crime
আপনাদের শিরোনাম টা এই ভাবে দিলে ভালো হতো ডিসির চোদা খেয়ে জ্ঞান হারালেন নারী সহকারী,1,crime
কিসের তদন্ত সবার সামনেই চোদাচুদি করছে শালার পুত কে ধরে লিংগ কাটাহোক সিসি কেমেরা কথা নাই বললাম,1,crime
ডিসির বৌ এখন খুব সুবিধা পাবে পর পুরুষের সাথে চুদাচুদি করতে পারবে,1,crime
মাদারচোদের বাচ্চাকে কঠিন শাস্তি দেয়া হোক,1,crime
মাদারচোদ নাকি হালায় পুটকি মারতে গিয়া ধরা খায়ছে।,1,crime
মিন্নি মাগির পাসি চাই এই মাগির কারনে আজ এত প্রান গেলো,1,crime
চোদানি তোরে বাঁচার মতো ব্যবস্থা করে দিবো তাইনা চোদা খাওয়ানোর আগে মনেছিলো না আর তোর আশেপাশে কর্মচারীদের সাথে খারাপ ব্যবহার করার আগে মনে ছিল না,1,crime
শালা জেনাহুর পাগল হয়ে গেছে,1,crime
তোমাকে জনগন চোদতে মাগি,1,crime
খানকিকে আবাসিক হোটেলে চাকরি দেওয়া হোক,1,crime
এই মাগি রিফাত হত্তার সাতে পারসন জরিত সেটা সুদু নয়ন বন্ড জানত,1,crime
মাগীর ঘরের মাগী,1,crime
বেশা মগি,1,crime
ওর সোনা কেটে ওর হাতে দেয়া হোক,1,crime
মাগিও রাখছে চুদার জন্য আবার ডিলার মারাই মেয়ে ডিলার বলে চুদে,1,crime
কতগুলো বেইসসার ছেলে,1,crime
সেক্স,1,crime
শুয়ারের বাচ্চা কার বিচার চাই,1,crime
বিক্রিতি রুচি সারাদিন যে মাগী এই টেবিল ঐ টেবিল কাজ করে বেরাই তাদের সাথে বড় লেবেলের হয়ে কি করে পিউন এর সাথে শুই!ছিঃ! ডিসির বৌ এর জন্য খুব কষ্ট হচ্ছে। সেম প্রবলেম আমিও ফেস করেছি। আজি যেনো এমন স্বামী কে ডিভোর্স দেয়। আমি দূর করে দিয়েছি আমার জীবন থেকে এমন কিট কে।🤬😡,1,crime
চুদির ভাইর আবার বিশ্রাম কক্ষ্য লাগে।।।শালারে জুতা মার।,1,crime
অচোদা কাজ করে। এখানে আইন চোদাস। এই রকম দেশের স্বাধীনতা এবং গনতন্ত্রকে লাথি মারি। পূর্বের পাকিস্তানি ভালোছিলো। বাংলাদেশ নামক দেশ হয়ে দেশটা বেহায়া হয়েছে। চোর চুরি করে চোর তদন্ত করে দেখবে কে চুরি করেছে। এ আজব নাটক। পাছায় ডিম ভরলে সব বাড়াবে।,1,crime
বানচোতের ধোন রেললাইনের উপর রেখে হামার দ্বারা পিটানো উচিত।,1,crime
চুতমারানি নটি পুটকিমারস আর কয়দিন দিসস ক আর বাচচা কয়টা ফালাইসস ক,1,crime
খানকির ছেলে যে ক্যামেরা লাগাইছে এটা তার দোষ না যে আকাম করছে সেটা তার দোষ। আকাম করলে অপরাধ নয় দেখলে অপরাধ।,1,crime
আপা কয়দিন খবর পরবেন তারপর ভূলে জাবেন আসল পদকতো বূকে পোদক নিয়ে কি হবে ডিসি চিনতা করে আরো নতূন মাল পাবো,1,crime
শালী তোর কারণে,1,crime
খানকির পোলারে জুতা পিটা করা দরকার,1,crime
সব সালারা লুইচ্চা,1,crime
ভাই মাল টা বডি টা আনেক ভালো লাগে তাই ডিসি সামালতো পারে নাই।,1,crime
শালা আবার কথা কয় কোন মুখে,1,crime
শালির ঘরের শালি তখন দেখি বোরকা খুলে মাতছিলি সাইয়ে তখন ঘামিয়ে কস বেরিয়ে ছিলো এখন দোস নাই চোতমারানি তোদের জন্য আজ দেশের এ অবস্হা স্যার চোদাস ও তোর তো দ্বিতীয় স্বামি দু টার ই শাস্তি হওয়া দরকার,1,crime
নয়ন আর রিফাত ছাড়া অনেক খানকির পোলা আছে যারা এর সাথে জড়িত। সব গুলারে বাইন্ধা একটা একটা রগ কেটে মারা লাগে।,1,crime
সালা আবাল চুদা কচুক্ষেতে গিয়ে ফাঁসি দিয়া মর।,1,crime
সালারা মুক্তিযোদ্বাদের নাম দুবাইস,1,crime
উপর আর নিচ কি মাদার এর বাচ্ছা,1,crime
একন বুঝেচি এই খানকির কারনে চেলেটির পান গেলো,1,crime
শালারে জুতা দিয়ে পিটাইয়ে দেশ থেকে বের করা উচিত।,1,crime
খানকির পোলার গোয়া দিয়া গরম ডিম ঢুকায়দে সবাই।,1,crime
তগরে জুতা মারার দরকার সালার পু তে রা,1,crime
ক্ষমা সুন্দর চোখে দেখার জন্য সবাইকে অনুরোধ করলেন। আবার দাবী করলেন এগুলো কারসাজি এগুলো এডিট করা যায় ভাই । আহসান হাবিব পেয়ার আর আমি কিছু কইলেই পাবলিকের পাছা পোড়ায়। পাবলিক এহন ঘুমায় তাদের হিসাব থাকে না।,1,crime
জানোয়ারের বাচ্চাদের ফাশি দেওয়া হোক তারাতারি,1,crime
ডিসি ষাঁড়ের ইন্টারভিউ এই ভিডিওগুলো কি আপনার ষাড় লা হাওলা অলা কুয়াতা এগুলো এডিট করা যায় আপনি তো এখন ভাইরাল প্রায় সেলিব্রিটি হয়ে গেছেন। আপনার অনুভূতি কি ষাড় চিল্লাইয়া মার্কেটে পাওয়া যাইবো মিনিট সময় দিলে মার্কেট পাওয়া যায়। আপনার রুমের পরিবেশটা কেমন ছিল ষাড় কোন হৈচৈ ছিলনা। শয়তানের দলেরা কবে ক্যামেরা লাগাইছে আমি কি জানি আপনার ভিডিও থেকে পোলাপান গুলি কি শিখতে পারল ষাড় বুঝলে বুঝ পাতা না বুঝলে তেজপাতা।লাইট বন্ধ না করে ক্যামেরা বন্ধ করা দরকার ছিল সবাই বলে আপনার মত গণ্যমান্য জঘন্য ব্যক্তি রাষ্ট্রের জন্য ক্ষতিকর আপনি কি মনে করেন ষাড় আমিও বলি আমি তো বালা না বালা লইয়া থাইকো। সকল অফিসে ক্যামেরা লাগিয়ে দিও নতুন কোন অফিসে চাকরি নিলে সেখানে কি ক্যামেরা দিয়ে দিব ষাড় শয়তানের দল আবার সাক্ষী হয়তি। আপনার খাওয়া দাওয়া চলে ষাড় ঢেলে দেওয়ার পর আর খাওয়া দাওয়া করিনি। সব মিলিয়ে এখন আপনার কাছে কেমন লাগে ষাড় আমি মার্কেট পেয়েছি। তোরা পোলাপাইন না থাকলে আমি শেষ। মাঝে মাঝে উপরে নিচে কিছু দেখুন লাগে 🙂🙂,1,crime
ওই ডাইনির ফাঁসি চাই,1,crime
জত সব পাগল ছাগল,1,crime
আমরা খতিয়ে দেখবো এটা বি এন পি র হাত আচে সালা এটা তদন্ত করবি আর না হলে কি করবি,1,crime
কিসের তদন্ত খানকির পোলা তদন্ত করলে তো তুই মাপ পেয়ে জাবি লজ্জা থাকলে এখানে এসে হাসতি না বেয়াদব,1,crime
এই জমুনা টিবির খানকির পোলারা আসল ঘটোনা তোলে ধরেনা খানকির পোলার কতো খাইচিস??? মিন্নি কি ডোকাইয়া দিছে তোদের কে,1,crime
ঐ শালির বেটি কি একজনের জন্য ষোল জনের ফাঁসি হচ্ছে।ফুরিয়ে মারছে যে দেখছ নাই,1,crime
সবগুলাই আচোদা,1,crime
মুক্তিযোদ্ধা ক্লাব নাম দিছে আসলে চুদাচুদির ক্লাব।,1,crime
স্যার তো আকামটা বেশি খন করতে পারলো ন সালা আগে জিনসন খেয়ে নিলে তো বিশিখন করতে পারতো,1,crime
এই কুত্তাকে সরকার এখনো চাকরিতে রাখছে কেন,1,crime
তোদের মত বেশ্যা মাগীদের জন্যই আজ পৃথিবীতে গজব আসতেছে এখন সরু কথা খানকি কোথাকার !!!!,1,crime
শালার দুঃখে মরে গেলাম এতগুলা মানুষ দাঁড়িয়ে দাঁড়িয়ে দেখল একটা মানুষ ফেরানোর চেষ্টা করলো না,1,crime
খানকির ঘরের খানকি সার না বলে অাব্বা বল বল তর বাপের কোনো দুষ নাই।,1,crime
মাদারচোদ কে লেংটা করে পিঠানোর দরকার।।,1,crime
শয়তান মাগি মিন্নি,1,crime
ছিঃ ছিঃ ছিঃ ছিঃ ছিঃ ছিঃ ছিঃ মরি তুই মরি যা লজ্জা ছিঃ ছিঃ ছিঃ কেমনে বউ বাচ্চাদের মুখ দেখাইবি কুত্তার বাচ্চা,1,crime
বাংলাদেশের সব থেকে বড় মাদারচোদ হচ্ছে পুলিশ ।।বাংলাদেশ সরকার যতদিন না পর্যন্ত এই মাদারচোদ পুলিশের সঠিক আইন না চালু হচ্ছে।। ততদিন পর্যন্ত এমন হতেই থাকবে।।বাংলাদেশ সরকারের প্রতি আহ্বান জানাচ্ছি ।।বাংলাদেশ পুলিশ মাদারচোদ দের মানুষ বানানোর জন্য,1,crime
নয়নের মায়রে চুদি খানখির পুলার ফাঁসি চাই আর মিন্নি বেশশার বাচ্চা যদি এই হত্যা কান্ডের সাথে জড়িত থাকে তবে তার ও ফাঁসি চাই নয়নরে আমারা দেখলে খোন কইরা ফাইলমু আইনের মায়রে চুদি,1,crime
এই মাগিরে এরুম কইরা ভিডিও বানান উচিত।আর চাইডের কুত্তার বাচ্চারা কি করচে???🐕🐕🐕,1,crime
এই কুত্তার বাচ্চারা সবাই টাকা হারে তাহলে তোর কোন বাপেরা জিতে শালার ব্যাটারা আসলে এটা প্রশাসনের দোষ কিন্তু জানি এখানে জুয়া খেলা হয় তারা কোনো পদক্ষেপ নেয়নি যার ফলে আমাদের বাংলাদেশ এতগুলো লোক এই খেলার সঙ্গে জড়িয়ে গেছে আমি প্রশাসনকে বলবো এখানে প্রশাসনের লোক খেলতে আসে একজনের মুখে শুনলাম প্রধানমন্ত্রী শেখ হাসিনাকে অনুসরণ করে বলছি আগে যে প্রশাসন এখানে জগতে আসে তাদেরকে ধরা হোক,1,crime
কুত্তার বাচ্চা মহিলা একটা তার নাকি একটা বাচ্চা আছে আবার অন্যজনের সাথে কুকাম করে বেড়ায় ব ম ! 😡,1,crime
বলদ চুদারা বালের ভিডিও বানায়।,1,crime
মাগি একটা একে পাথর মেরে হত্যা করা হোক,1,crime
মাগিখোর আবার ডিসি হয় কি করে ওই হাসিনা!,1,crime
ভাই এই মেয়ে জড়িত সেটা আমি ভালো করেই জানি এই মাগি ছেলেটাকে মড়ে ফেললো আরফিন শুভ ভাইএর মতো দেখতে ছিলো ভাইয়াটা,1,crime
মানুষকে এত বোকা নাকি তার কথা বুঝবে না তার অফিসের নারী তার রুম তারে অফিস এখনকার লোকগুলোকে বোকা যে বোঝেনা ভালো মন্দ এই শালায় কাজটা করছে মানুষকে বোকা বানাতে চায়,1,crime
শালা ডিসিরে! বউ নাই তুর বাসায় ছি ছি ডিসি।,1,crime
কি সুন্দর একটা কি ঘটছে তা নিয়ে মিডিয়ায় মাদারচোদ রাজি কাহিনী চোদাচ্ছে মিডিয়া মাদারচোদ বউ পরকীয়া করে আর এক সাংবাদিকের লগে তারার খবর নাই পরে বগা ধইরা টানাটানি করে,1,crime
আবালগো খাইয়া কাজ কাম নাই এখন এইগুলাই করবো। যতসত আবালের দল। রিপোর্ট মারেন সবাই,1,crime
শালী তোর কপাল ভালো যদি আমার এলাকায় হতি তোকে আমি বডি দিয়ে কোপাইতাম,1,crime
শুধু মামলা নয় ফাঁশি চাই সবকয়টার। মিননি খানকির ফাঁশি চাই।,1,crime
শালা এতদিন শুধু মোবাইলে জুয়া খেলছি বাস্তবে খেলিনায় তাই সরকারের কাছে আবেদন জুয়াটা বৈধ করা হোক সাথে মদ তাহলে অন্তত ইয়াবা খেয়ে বাংলার তরুনপ্রজন্মের ছেলেপেলে একেবারে ধ্বংস হবেনা।,1,crime
মাগি নাটক করের,1,crime
মাগি ডুকাই ছেজে ঐ সময়তো আরাম লাকছে তোর কাছে,1,crime
এই সব কুক্তার বাচ্চারা ওই দেশটা কে আরো নষ্ট করছে,1,crime
সালার বেটার শরম নেই আবার মিডিয়ার সামনে কথা বলতে এসেছে। আর ক্যামেরার সামনে শুধু ডিসিকে কেন আনা হলো মহিলাকেও আনা উচিত ছিলো।,1,crime
একে জন সাধারণ কে দেওয়া হক আমরাও একটু পেনটি খুলমু,1,crime
কুত্তার বাচ্চারা তোমগো সামনে তোমগো বন্ধুরে মারছে আর তোমরা খাড়াইয়া বাল ফালাইছো,1,crime
বাংলাদেশের রন্দে রন্দে লুচ্চা বদমাশ বেশরম বেহায়া কুলাংগার দের কে বসিয়েছে বিনাভোটের সরকার ভোট চোর,1,crime
যে ক্যামেরা টা লাগাইছিলো তার বিচার আমিও চাই সালা ক্যান ক্যামেরা লাগালো না😁😁😁,1,crime
ভাঙ্গিস শালা ডিসির মুখে দাড়ি নেই,1,crime
মাগি কয় কি মাগির মনে হয় আরো একশ জনের চুদা লাগবে।কি বলেন আপনারা।,1,crime
সালা নিশাখোর,1,crime
এই কুত্তার বাচ্চাদের আগে মনে ছিলনা। যখন নিষ্পাপ একটি মেয়েকে কেরোসিন ঢেলে আগুন ধরিয়ে মারা হলো। তখন এই কুত্তার বাচ্চাদের সবার মনে ছিল না। বলে আমাদের পরে কি হবে। তাই বলবে কুত্তার বাচ্চাদেরকে জনতার সামনে ফাঁসি দেওয়া দরকার। যেন এদেরকে দেখে আর বাকি লোকগুলোই এমন কাজ না করতে পারে।,1,crime
কোথার বাচ্চা শুরুর বাচ্চা তোর মত সন্তান জন্ম দেয় বেশা মেয়ে রা,1,crime
মুসলিম হোক যাই হোক আমরা তো সবাই মানুষ 😭😭ভিডিওটি দেখার পর চোখে জল নেমে আসল 😭😭আর মানুষ এতই স্বারথপর হয়ে গেছে 😭😭😭সবার সামনে রিফাতের খুন হচ্ছে এথচ কেই এগিয়ে আসলো না😭😖😭 যদি সবাই যদি এগিয়ে আসতো রিফাতের এভাবে যগন্যো মৃত্যু হতো না 😿😹😭👉👉আমি সরকারের কাছে এই বিচার চাই রিফাত💗💗 ভাইয়াকে👉👉 যেভাবে খুন করেছে তাদের যেন সঠিক বিচার হয় 👍👍এই কামনা করি আর বিশেষ করে মিন্নির ফাসি ফাসি হোক 👤😣😈😈কারণ ভিডিও🔭📱💻 টি ভালোভাবে দেখার পর জানা গেল যে মিন্নি 😈😈 কেন আরো বেশি হাত আচ্ছে 👤এই রিফাত ভাইয়ের❤❤ খুনিতে কারন আপনারা সবাই ভিডিওটি ভালোভাবে লখ করুন👍👍 রিফাত ভাইয়া💟💟 আসার পর মিন্নি কে যাওয়ার জনোও ডাকে মিন্নি রিফাত ভাইয়ার 💗💗সাথে না গিয়ে ওই জানুয়ারদের🐺🐺🐺 কাছে চলে যায় ওই জানুয়ার রা 🐺🐺🐷যেন জানে রিফাত ভাইয়া💝💝 সঠিক সময়ে আচ্ছে এই বলতে গিয়ে 😈😈বেয়াদব মেয়ে মিন্নি টা দুরে গিয়ে 👉রিফাত ভাইয়ার💝💝 সাথে না গিয়ে আবার কলেজের ভিতরে ধুকে পরে👉👉 বেয়াদব মেয়ে ধুকার পর রিফাত💕💓 ভাইয়াকে এসে সবাই মারতে শুরু করে 😭😭আর যখন রিফাত ভাইয়া কে ধরে নিয়ে যায় তখনও সেই দেখেই কিছুই করলেন না😭😖😭😭😭😭 তার পিছু পিছু আস্তে আস্তে হাটতে লাগলেন😈😈 আর যখন জানুয়ার রা✂📌📍🐶🐹🐺🐺 রিফাত ভাইয়াকে💗💗 কুপাতে শুরু করে 😭😭মিন্নি নামে বিয়াদব মহিলাটা তার কাহিনি শুরু করে দরশক ও মিডিয়ার সামনে তার সাধুটা প্রকাশ করে 😈😈 নিজে বাচ্চার জনোও যাহাতে ওর সনএাসের প্রতিরুপ যেন কেই বুজতে না পারে 😈😈👣👣👣👉👉আমার বলার এই যে রিফাত ভাইকে 💝💝💞যারা খুনি করেছে সরকার তাদের সবাইকে যেনো ফাসি দেই😈😈 আর মিন্নির মাগিকেও ফাসি চাই😈😈😈 জনগনবসবাই চাই মিন্নির সাথে যারা জরিত তাদের ও এই ফাসি হোক 😈😈কারন এই বিচারটি যদি সুস্তভাবে না😭😭 হয় মিন্নির😈😈 জনোও আরো অনেক ভাইদের জিবন হারাবে 😭😭😭আমি চাই মিন্নির ফাসি ও তার সাথে যারা জরিত তাদেরও ফাসি হয়ে😈😈 রিফাত ভাইয়ের আত্তা শান্তি হোক💓💟💕 এই কামনা এই বিচার যেন সরকার মেনে নোক👏👏 এই বিচার সকল জনগনের দাবি 👏👏👏👏 এই বিচার করুন সরকার আর জনগন👏👏👏 এই ভিডিওটি যিনি উপস্তাপন করেছে তাকে অনেক ধন্যবাদ👏👏💟💞💝,1,crime
সালা সবাই তাকিয়ে দেখলো লোক কে কুপিয়ে হত্যা করছে কিন্তুু কোন জানোয়ারের বাচ্চা ছেলে টা কে বাচাতে এগিয়ে আসলো না,1,crime
দুনিয়ার মানুষ চোদাচুদি করে দোষ হয়না ছাত্র চোদে নাউয়া চোদে হুজুর চোদে সাংবাদিক ও চোদে খালি ডিসি চুদলে দোষ হয়,1,crime
তোদের মত বেশশা খাংকির সামান্য চাকরি জন নিজের ইজ্জত দেহ বিলিয়ে দিয়ে এই ডিসি মত অসৎ দুর্নীতি চরিত্রহীন মানুষকে খুশি ফুতি আনন্দ রংগলীলা করার জন ভোগের পাঞী তোর স্বামী সন্তান আজ কোন মুখে তোর পরিচয় দিবে তোই নারী নামের কলংক,1,crime
শালার নুনুর ঘোডা কেটে দেওয়ার দরকার।,1,crime
বয়স তো কম হয় নাই এখনো লুচ্চামি করস লজ্জা করে না কিভাবে তোর ছেলে মেয়েদের সামনে মুখ দেখাচ্ছিস নির্লজ্জ বেশরম কুত্তার বাচ্চা,1,crime
কুত্তা সাংবাদিক। এই মেয়েটাকে আর বেচে থাকতে দিবে না।,1,crime
মাগী মুখ ডাকে বোদা খুলেদে ব্যশা মাগী,1,crime
সালা মাগী চোদা লোক প্রশাসন ক্যাডারের বদনাম করলি তুই,1,crime
কুত্তার বাচ্চাকে গুলি করে মারা হোক,1,crime
আরে এইসব আকাম কুকাম সবাই করে। দেখা যায় তুইও করছোছ কিন্তু এখন সাধু সাজছোছ। আমরা কেউ ই ধোয়া তুনসি পাতা না।এই খানে যারা কমেন্ট করতেছে তাদের ভেতরে অনেকেই এইরকম কাজের সাথে জড়িত সে মেয়ে হোক বা ছেলে। অহরহ স্কুল কলেজের ছেলে মেয়েরা রিক্সা সিএনজি গোপন বাসা বা হোটেল পার্ক ইত্যাদি জায়গায় গিয়ে যৌবনের রস বের করছে।তাই বলব এইগুলা কখনো বন্ধ হয়নি আর হবেও না।।আর তুই খানকির পোলা এই সুযোগ গুলা কাজে লাইগাইয়া ভাইরাল হওয়ার ধান্দা খুজোছ বাইনচোদ। আরে খানকির পোলা তোর নিজের ই তো ঠিক নাই। দাড়ি রাখছোছ তাও আবার স্টাইল মারাইয়া একটু।তুই নিজে ঠিক হ আগে বেজন্মার বাচ্চা।বেশি সাধু সাইজো না নিজে চোদনা।তোর পরিবারের ভেতর ও অনেকে এইগুলা করে বেড়াইতেছে যাইয়া দেখ। এই জিনিস গুলা আজকে নতুন না অনেক পুরাতন তাই কোন আইন করে এইগুলা বন্ধ করা যাবে না। যতদিন না মানুষ ব্যাক্তিগত ভাবে ঠিক হবে ততদিন এইগুলা চলবে।,1,crime
ডিসিতে চুদলে আইনে আছে আর গরিবে চুদলে বিচার আছে,1,crime
মাগী খানকি তোকে জাহান্নামের লাকরী বানানো হবে,1,crime
ওই পা চাটা কুত্তা ফুল ভিডিও পোস্ট কর মাঝখানে কেটে কেটে কেন ভিডিও পোস্ট করছিস মিনি কি তোরে রাত্রে বেলা থাকতে দিব,1,crime
সব কুত্তার বাচ্চাদের ফাঁসি দেওয়া হোক প্রকাশ্যে আজ সোনার বাংলার এই অবস্থা ওই কুত্তাদের জন্য,1,crime
এই হলো বঙ্গদেশের অবস্থা। ডিসি যদি এইরকম লুইছা হয় তাইলে দেশের কি ভবিষ্যত সালার চেহেরা শয়টানের মতন,1,crime
শালী চুতমারানি এখন মিথ্যা কথা বলিছ। চিন্তা করিছ না। আওয়ামী লীগের সরকার আছে তোদের পাশে।,1,crime
কিচ্ছু করার নাই কুত্তা লিগের দল,1,crime
ভন্ড লুচ্চা শালারে জুতা মারো,1,crime
ইছ চুতমারানি মাগী আবার নাটক চুদায় খানকি,1,crime
সাংবাদিক তরা আগে কি বাল ফালাছো।,1,crime
গানই হোনান আর কি বালডা ফারবেন 😂😂,1,crime
মসজিদের সহর মাগিদের আড্ডা জুয়ার আড্ডা আবার মাগিরা বলে নাকি ডিলার শিপ মাল ঠিক আছে,1,crime
এদের কিছুই হবেনা এরা জানোয়ার লীগ,1,crime
শালারে গণধোলাই দেওয়া দরকার,1,crime
সালা বদমাইশ মাগির পোলা,1,crime
এই গুলা এডিট করা যায় শালার পুতরে রিমান্ডে নিলে সব বেরিয়ে আসবে,1,crime
এই শয়তান মেয়েটাকে দেখতে মনে চায়না ওর মুখে ওয়াক থু,1,crime
নটি মাগি তখন তো হোগা ভিজেগেছিলো পানিতে এখন ঠেলা সামলা ভিডিও ধারনকারি ভাইকে নবেল দেয়াহোক,1,crime
ঐ খানকি যে বলল ওকে জোর করে ভয় দেখিয়ে সাইন নিছে কিন্তু এখানে তো অনেক আনন্দ করতেছে এটা কেমন করে,1,crime
ও ছামায় আইক্কাওলা বাস দেওয়া দরকার,1,crime
শালারা মিননির দালাল,1,crime
চোরের দিন গৃহস্থের দিন দেখ মাগী কেমন লাগে,1,crime
বালের ভিডিও বানায় এসব তো আমরা সবাই জানি !,1,crime
মাদার চুদ তুই এগুলা বলে তুর মারে গালি শোনাতে চাস কেন ডিসি হয়ে এগুলা করবে কেন সি সি ক্যামেরা লাগাইছে তাতে ধরা পরলো যে আইনের লোক হয়ে এগুলা করে এখন সাধারন মানুষ হলে এখন অনেখ কিছু হয়ে যেতো ডিসি কে আর মেয়েটা কে আইনের আওতায় আনা হউক একমত হলে লইক দিন,1,crime
মাগির বিচার চাই,1,crime
লুচ্চার মাজায় জোর নাই এই মাল চালায় কিভাবে মনে হয় আমার দরকার পরতো পারে এই মালের,1,crime
ভোট চুরি করে আওমীলীগ খমতাই এসে আজ পযর্ন্ত শিকার করলে না আর এই চুদনা শিকার করবে হা হা হা,1,crime
হাস্যকর 😂😂😂 তোরে কুঠি মানুষ চুলরেও তোর শরম হবেনা খানকি প্রমোশনের আশায় স্যাররে চুদাদিতে দিছিলি বা একবারের জন্য তোর হাজবেন্ডের হকের কথা ভাবলিনা তোদের মতন মানুষের জন্য আচ দেশের এই অবস্থা,1,crime
দেশের আইন যে সবার জন্য সমান নয় এখানেও আবার প্রমাণিত! এই মাদারচোদ এখনো স্বপদে কিভাবে আছে 🧐🤥😡,1,crime
যারা সময় মত বয়াসে দাড়ি না লাকে কেটে এবং সেফ করে তাদের মোখ দেকতে মহিলার ভুদার মত লাগে মহিলাদের ভুদার বাল কারলে যেমন লাগে তেমনি ডিসির মোখটা সেরকম রাকছে,1,crime
চোদমারানি তাহলে ত সব ছেলে মেয়েরা পার্কে গিয়ে চোদাচুদি করবে আইন ব্যবস্তার ত কোন দরকার নাই,1,crime
বেয়াদবের বাচ্চা বেয়াদব হ্যাকার গ্রুপ বর্ণনা হ্যাকার গ্রুপ বার করে দিব লুচ্চামি কি করস শরীরটা দেখছিস নিজের ছবিটা দেখ,1,crime
জুতা মার শুয়ারের বাচ্চারে,1,crime
মাগী চুদা দেওয়ার সময় মনে তাকেনা সন্তানের,1,crime
এই শালা একটা লুচছা পথমে তাকে চাকুরি বাতিল করা হোক পরে পাচাই বাঁশ দয়া হোক,1,crime
অনুরোধ যখন করেছে তাইলে প্রকাশ চোদাও কেন,1,crime
জামালপুর তো পতিতা বেশি তাই এরকম হয়ছে,1,crime
বেইশ্যা মাগী,1,crime
এই কুকুর বাচ্চা৷ জুতা৷ মারা৷ হক,1,crime
শালা আবাল চোদা রা,1,crime
তোরে এখনো তোর স্বামী তালাক দেয় না মাগী আর সন্তান কার এটা আমার প্রশ্ন আমার মনে হয় কাকের বাসায় কোকিল ডীম পেরেছে।,1,crime
দানব দের ফাসি চাই।। না হলে জনগন একদিন ওদের কে গনদোলায় দেবে,1,crime
ভাই আপনি আমার বাল এর ভিডিও বানিয়েছেন চোর কোনদিন চুরি করে বলে কি? যে আমি চুরি করেছি আবাল তো আবালই আপনি একটা আবাল,1,crime
সালা লুচা,1,crime
শালা বাঁচার জন্য এখন নাটক করতেছে ।,1,crime
এই কথাটা সত্য কথা মাগির ফাঁসি চাই এবং দ্রুত বিচার করতে হবে,1,crime
খানকির পোলারে প্রশ্ন করতে মাল পড়ে গেছে। সব জায়গায় ঢেলে দিতে মন চায় মাগির পোলা,1,crime
ভিডিও নাকি হাত দিয়া বানান জায় ওরে আবার কেউ হিজাব সহ চোদরে ভাই,1,crime
সালা চুদতে পারে না,1,crime
মিন্নীর নয়নের সাথে গোপনে বিয়ে হয়েছে সরকারি কাজী এ বিয়ে সম্পন্ন করেন। এই শালী পরকিয়া প্রেমে জড়িত ছিলে। এই সব খারাপ মেয়ে দের কারণে এরকম ঘটনা ঘটে থাকে। এই শালীকে রিমান্ডে নেওয়া হোক,1,crime
লুইচচা বদমাইশ গুলারে দিয়া দেশের উন্নয়ন হবে কুত্তার মতো সমাজ নষ্ট হয়া জাইবে । বদমাশের বাচ্চা বদমাইশ,1,crime
এইমাগিআগেথেকেবাইরেখাওয়ারঅববাস।এককলায়মাগিরহয়না।,1,crime
ছি কুত্তার বাচ্চা তুদের জন্য দেশ অনেক পিচিয়ে আছে,1,crime
মাগিরে পতিতা পলিতে বিকরি করে দেয় তার এলাকার মানুষ কোথায় এরা কেন ঘুমায় একটা মলি মানুষ জদি কিছু করে তাহলে এলাকার মানুষ সবাই আনোলন করে এখন কোথায় তারা,1,crime
মাগি পতিতালয়ে যাও বাঁচতে পারবা,1,crime
সালা মাগি খোর,1,crime
এই খানকির পোলার জন্য দেশের এই অবস্থা শালারা ঘুষখোর,1,crime
আমাদের সুন্দর দেশটা কিছু মানুষ রুপি কুত্তার কারনে ধংশের পথে আল্লাহ আমাদের সহিহ বুজ বুজার তাওফিক দান করুন আমিন,1,crime
আবালের দল বাল বানাইছো বালের মত হয়েছে তোমাদের ভিডিও,1,crime
ওর ধোন কেটে দিন,1,crime
সু প্রিয় দেশবাসী আমরা বাংলার সকল নাগরিক এ মিন্নি নামক পতিতাকে ফাঁসির কাষ্টে দেখতে চাই যাহাতে এইরকম মিন্নি আর বাংলার ঘরে জন্ম না নেয়,1,crime
সালায় একটু খেলতেও পারল না অথচ দোষ পরল 😂😂,1,crime
খানকির পোলা ভালো মানুস আসামি করিস আর খারাপ গুলা ছেড়ে দেছ,1,crime
সালার বাই এত কতা না বইল্লা ফাসি দিয়ে দিলে ঐ তো চলে,1,crime
খানকির আবার চোদা খাবে।,1,crime
শালা লুচ্চা হ্যাকার মেকার কিছু না এই নারীর সাথে লুচ্চামি,1,crime
কুত্তার বাচ্চা,1,crime
মিন্নি মাগিরে ধইরা উলঙ্গ কইরা বাইরালে সব বলে ফেলবে ঐ মাগি ঘটনার মূল কারন,1,crime
চোব চুতমারানি স্যারের কোনো দোস নাই আমার কি কানা আমরা কিছু দেখি নাই চুতমারানি তোগোর জন্য হাজার হাজার কর্ম জীবি নারীর কল্ক 😡😡😡😡😡😡😡😡🚬🚬🚬🚬👿,1,crime
হায়রে মাদার,1,crime
তার নিচে রট গরম করে দিলে সব বের হয়ে আসবে খানকি নটি বেসা এমন একটা ফুলের মত ছেলেটাকে জীবন দিতে হল,1,crime
ত রা পুটকি মারা খা সালারা,1,crime
খানকি চোদা মাগি তুই কি মা নাকি তুইতো মা নামের কলঙ্ক আবার সন্তানের দোহাই দিচ্ছিস সন্তানের কথা আগে ভাবিস নাই মাগি যে তোর নষ্টামির কারনে তাদের জীবনে কি প্রভাব পরতে পারে । আবার বলছিস সন্তানের মুখের দিকে তাকিয়ে বেচে আছিস । মাগি এখন যে মানুষ তোর সন্তানকে বলবে না যে তোর আসল বাপের নাম কি এর কি গ্যারান্টি আছে,1,crime
সব গুলো মিথ্যুক মাদার চুদ ওরা সবাই জানে ওখানে খারাপ কাজ হয় তার পরও এখানে আসে ওরাই তো দেশের পরিবেশটাকে নষ্ট করতেছে ধন্যবাদ আপনাকে ও রেবেের ভাইদেরকে,1,crime
এই লুচছা দরা খায়ছে কেউ একে জুতা দিয়া মার নেইলে ওর চেম কেটে দিয়ে হিজলা বানিয়ে দাও,1,crime
রিফাত দুনিয়া থেকে বিএদায় নিয়েছে বলে তুই মাগি মিথ্যা কথা বলে পার পেয়ে গেলি রিফাত তার বাবার কথা বলেছিল নাকি তকে নিয়ে বাসায় যেতে চেয়েছিল।,1,crime
এই মাগী তোমার ভিডিও বানিয়ে করছে তুমি বলছ মাগী খানকি মিনিট চুমা চুমি করছো ইস্পট দেখ জাচ্ছে আবার বানানো ভিডিও মারাও মাগী,1,crime
এই লুচ্চা লাফাঙ্গা গুলোর বউ সুন্দরী হয় তাও কেন যে ছোটে জরিনা সখিনা মর্জিনার পেছনে আল্লাহ ভাল জানে।আসলে কুত্তার পেটে ঘি হজম হয়না।যদি যোগ্যতা সহিত ডিসি হত তাহলে তার মান রাখত ডিসি হয়েছেত ঘোষ দিয়ে।,1,crime
সকল ভাই এবং বোন ঐ মাগি বিচার চাই এক জনে কেন ও চুদা দিল বাকি সবাই কেন ও চুদা দিল না এ জন্য বিচার চাই।,1,crime
ওদের জন্য কান্না করে কুনুভাল নাই কারন এরা মানুষ রুপি জানোয়ার,1,crime
এই খানকির পোলারে বরখাসতো করা হোক,1,crime
এইরকম লুইচ্ছা বদমাইশ খানকির পোলাদেরকে জোতাপিটা করে অফিস আদালত থেকে বের করে দেওয়া উচিৎ।,1,crime
এই হালার চেহারা দেখে মনে হচ্ছে বুশ হালায় ঘুষ খেয়ে বুশ হয়েছে।,1,crime
মাগি তোরে কিছু করেনায় চোদ ছে,1,crime
শালার ঘরে শালা মিন্নি তর মাগি লাগে,1,crime
বোকাচুদা আবার মুখ দেখায় কেমনে,1,crime
আমরা চাই ওই মাগির ফাঁসি দেওয়া হোক,1,crime
যদি মুন্নি এই হত্যার সাথে জরিত থাকে তাহলে তাকে এমন ভাবে শাম্তি দেওয়া হক যানো ভবিষ্যৎতে কোন মেয়ে অার স্বামী রেখে নষ্টামি না করে।মুন্নির মত দেশে প্রায় মেয়ে অাছে যাদের বলা হয় প্রেমিকা রুপি খানকি।এইরকম মেয়েদের জন্য অাজ যুব সমাজ ধংস্ব।সংসারে অশান্তি। অার বিয়ে করতে গেলে কোন স্বতী নারী পাওয়া যায় না। তাই সরকারে উচিৎ পরকিয়া প্রেমের অভিযোগ পেলে অাইনত ব্যবস্থা করা। সরকার যে ভাবে সরিষা অভিযান চালিয়ে দেশ থেকে জঙ্গি শেষ করেছে।ঠিক ঐ ভাবে য়দি দেশের প্রত্যেকটা পার্কে ও লিটনের ফ্ল্যাট নামক ঐ রকম রুম গুলোতে যদি প্রতিনিয়ত অভিযান চালাতো তাহলে খুবিঈ ভালো হতো।বেঁচে যেতো হাজারো যুবক যুবতীর চরিত্র।,1,crime
ডিসি কুত্তার বাচ্চার বাড়ীর গ্রামের মহল্লার সকলের হাতে হাতে বিডিউটি পৌছানো হোক ওনারা দেখুক তার উলঙ্গ কুলাঙ্কারি। তারে জুতা দিয়া পিডা। আর মাগির বিডিউটা তার বাচ্চাদের সামনে তুলে ধরা হোক তাহলেই লাজ হবে।,1,crime
চুদার সময় মনে ছিল না,1,crime
এর জায়গায় যদি সাধারন কেউ হত তবে এতো ক্ষনে মিডিয়া ও পুলিশের ঠ্যালায় ঘুম হারাম হয়ে যেত আর চোট্রা শালায় পাঞ্জাবি পরে টল মারছে আমি দেখেছি ভিডিও টি ওটা ওই,1,crime
আরে বুকা চুদা ভাইরে নিয়ে গেলেনা কেনো,1,crime
এটা হাসিনার উন্নয়নের অংশ খানিকর বাচ্চা হাসিনার ভোদা চাট,1,crime
এই সব ডি সি মাদাসুদের জন্য বাংদেশে সুন্দরী কোন মেয়ে পাই নাই সব বুগ করতেছে। আর ঐ সব মগিরা উপরে উটার জন্য বছরের বুড়ার সাথে সুদা দিতে রাজি আছে। ধনে জোর থাক বা না থাক। প্রয়জনে নিয়ে সুয়ে থাকবে।তার পরেও উপরে উটতে হবে। আর এই সব ইছি ডি সির মত জত মাদার সুধরা আছে। বাংলাদের সুন্দরী মেয়েদেরকে ভোগ করতেছে। সুনার বাংলা একন আর নেই বুধার বাংলা হয়ে গেছে।,1,crime
বিষ খেয়ে বা গলায় ফাস দিয়ে মরে যা কুলাঙ্গার ডিসি। তোর বেচে লাভ কি 🙊🙊🙊🙈🙈🤐🤐😡😡,1,crime
এই করবে সেই করবে শেষ পযন্ত বালও করবে না,1,crime
মানে দিছি চোদা দিছি চোদা🤣,1,crime
কুত্তার চেয়েও খারাপ হয়ে গেছিস,1,crime
শালার পুতেরা এখন কান্দো কেন যখন নাকি নুসরাতকে পুড়িয়ে মারলা তখন মনে ছিল না যে পাপ বাপকে ছাড়ে না এখন কেন্দে কোন লাভ নাই ওপারে গিয়ে আরো কঠিন শাস্তি পেতে হবে এরকম কান্দা নুসরাত ও কাঁদছিল তোরা শুনিস নি আজ তোদের কান্না কেউ শুনবে না একেই বলে আল্লাহর বিচার,1,crime
জাতের মেয়ে কালো ভালো নদীর পানি ঘোলা তোর কারনে ম নষ্ট হলো দুইটি ছেলে পোলা আমি যদি পাইতাম তোরে তোর বোদার ভিতরে ঢুকাইতে মামি মুলা খানকিমাগী রূপের অহংকার করিস চুতমারানি ব ম তোর ভুদার ভিতর আঙ্গুল ঢুকিয়ে তোর মাসিকের রক্ত তোর মুখে খাওয়ানো উচিত তোমাকে যেন প্রত্যেকটা মায়ের ঘরে একটা না হয় তোর মত মানি হলে দেশের ছেলে একটাও থাকবে না তোর মত মাগির যারা আছে তাদেরকে আমি ধিক্কার জানাই তোদের মত মাগির সাওয়ার ভিতর চুতরাপাতা ভরা উচিত মরিচের গুঁড়া দিয়ে তোর বোদার ভিতরে তরকারি রান্না করে সেই তরকারি তোর চৌদ্দগুষ্টি কি মাসিকের রক্ত দিয়ে একসাথে খাওয়া উচিত খানকিমাগী এই বাংলার ঘরে যেন আরেকটা অনলাইনে শুধু একমাত্র তোর মায়ের পেটে যেন দেয় ব ম তোর মত খারাপ মেয়ে এই বাংলায় নেই যত নষ্টের গোড়া হচ্ছে তুই তোর ভিডিওটি আমি দেখেছি তোর হাজবেন্ড কে যখন ওর আমারে তুই দাড়িয়ে ছিলি তোর মতো নাকি ফাঁসি হওয়া উচিত সরকার যদি তোর ফাঁসি না দেখ তোর পক্ষপাতিত্ব করবে সরকার এটাই হচ্ছে কথা তোর মত মাগির আসলেই ফাঁসি হওয়া উচিত গিয়ে চোদাখাওয়ার যোগ্যতা রাখিস তোর মত আমি এই বাংলার একটাও যেন না হয় তোর মত মেয়ে যদি হয় দুনিয়াতে কোন ছেলে থাকবে না সবাই ধ্বংস হয়ে যাবে শুধুমাত্র রূপের অহংকার এর কারণে হে সুন্দরী নারীরা তোমাদেরকে বলছি রূপের অহংকার টা বাদ দাও মনের মিলন আজ থেকে বছর বছর পর চলে যাবে কিন্তু একটা কথা মনে রেখো মনের মিলন কখনোই যাবে না এটা হচ্ছে মূলত বাস্তব কথা আমার কমেন্টে কেউ কষ্ট পেয়ে থাকলে আন্তরিক ভাবে ক্ষমা চেয়ে নিচ্ছি সকলে ক্ষমা সুন্দর দৃষ্টিতে দেখবেন আশা করছি আজকে খুব কষ্ট নিয়ে এই কথাটুকু লিখতে হচ্ছে কারণ সম্পন্ন দুষ্টামির এ মেয়েটা সম্পন্ন মেয়েটা প্লান করে ছেলেটি কে মারিয়েছে ভিডিওটি আমি দেখেছি খুব ভালো করে নিজের চোখে সিসি ক্যামেরায় ভিডিওটি ধরা পড়ে সেই ভিডিওটা দেখতে পেয়েছি আরও অনেকগুলা সামাজিক যোগাযোগ মাধ্যমে আমরা অনেক ভিডিও দেখতে পেয়েছি তার মধ্যে সম্পন্ন বুঝা যায় যে তাই তাই সম্পূর্ণ দায়ী সকলে ভাল থাকুন সকলের সুন্দর জীবন কামনা করছি আল্লাহ হাফেজ,1,crime
কুত্তার বাচ্চা ফেক ভিডিও বানাস কেন?এরা নুসরাত হত্যা মামলার আসামি?,1,crime
তোর মাগি,1,crime
চোদানি মাগির তুমি পড়াশোনা কেন এখনো কেন মানুষ নাই,1,crime
তদের মত নটি দেশের বাইরাছ সমাজ নস্ট করস কে বলছে তকে বাঁচতে,1,crime
তুই মজা লুটবে আর হেকারদের দুষ শালা আবাল,1,crime
বালের ভিডিও ভুয়া ভিডিও বানাবেনা,1,crime
স্যার যখন ষাঁড় হোয়ে তোমারে ললিপপ বল বানায়ছিল তখন কই ছিল তোমার এই সন্তানের চিন্তা তোমাকে সবাই তারা রেট দিয়ে দিছে।তুই নেক্সট সানিলিওন।খেলা হবে ।।,1,crime
মিন্নি বেশ্যারে রিমান্ডে নিয়ে গরম ডিম দেয়া হোক। তাহলে অনেক তথ্য বেরিয়ে আসবে।চরিত্রহীন মাগী একটা। নাংগের আশায় ভাতার মেরে এখন অভিনয় চোদাইতেছে। এক খানকির জন্য দুই দুইটা জীবন ধ্বংস হয়ে গেল।,1,crime
তরে কুত্তাদিয়ে চুদা,1,crime
খানকির পোলা কতবড় নির্লজ্জ তার লাজ্জ নামক শব্দ টি তার জানা আছে বলে মনেহয় না।,1,crime
জানোয়ার,1,crime
সালার পুত অন্য চ্যানেল এর ভিডিও থেকে ভয়েস চুরি করে আপলোড করেছিস তুমি কি বোবা নাকি মাদারচুদ যে অন্যের ভয়েস চুরি করেছিস।,1,crime
পিঅন মাগি যেখানে সেখানে চুদা খাউয়ার জ্ন্য পিঅন হইসে,1,crime
বুদার খবর দেও। এই দেশ এ তরাই ত খারাপ। যখন এই গুলা শুরু হলো তখন কি করছিস।নাকি এখন টাকা দেই নাই,1,crime
শালি চাকরি করতে এসে নষ্টামি করে।।কেনো খালা খালু ঠিক মতো দিতে পারে না। ছি ছি আপনাদের মত নারীর জন্য আজও নারীরা কঙ্ককিত।।তোরে তো জুতা পিটা দেওয়ার দরকার।,1,crime
এইসব কুলাঙ্গারদের কে জুতা মালা দিয়ে ঘোরানো দরকার,1,crime
খানকি মাগি সন্তান চোদাও বেশ্যা মাগি,1,crime
কি সুন্দর আমাদের দেশ অফিসে নারি নিরজাতন করে কুকুরের বাচচারা জারজ,1,crime
কুত্তার বাচ্চাদের নজীরবিহীন শাস্তির ব্যবস্থা করা দরকার,1,crime
তুই মরোশ না কেনো তুই একটা খানকি,1,crime
হালার পুত দরা খাইছে সেটার বিচার না করে কে ভিডিও করছে তারে খোঁজে বের করার চেষ্টা করছে,1,crime
মাগীরা বেশি করে লাগাবো,1,crime
এসব খানকি মাগির লাইগা এই দেশের এই অবস্থা আরেক চুদানির পোলা ডিসি ওর পুটকির মধ্যে ভইরা দেওয়ার দরকার দশ ইঞ্চি বিচি 😁😁,1,crime
এইরকম কুলাঙ্গার জন্ম দিলে এই অবস্থায় হবে ফাসি তারাতারি হওয়া দরকার,1,crime
মিন্নি মাগী হইলো সব নাটেরগুরু ওর হাটা কেমন মনে হয় শুটিং করছে ওর স্বামীকে মারছে আর ও স্বাভাবিক থাকলো কেমন করে!! ওই জামাইকে মারাইছে ওর ফাঁসি চায় বাংলার মানুষ,1,crime
গরু ছাগলে বরে গেছে দেশ টা,1,crime
খানকি অবস্যয় জরিত খানকিরে ফাসি দেওয়া হওক,1,crime
ডিসি হিজরাহ হালার দোন নাই পতিতায় পাঠানো হক।,1,crime
বালের স্ত্রী। হাটার স্টাইল দেখছ?,1,crime
মাগির বোদায় মরিচের গুড়া মসলা ঢেলে দাও সব ঠিক হোয়ে যাবে😃😃😂😂,1,crime
এই মিন্নী মাগির বিচার না হলে আরও হাজার মিন্নীর জন্ম হবে।।।এইটা একটা রাস্তার মাগি,1,crime
আরে খাংকির পোলা মেয়ে অপরাধ দিস না আবালের মত,1,crime
মাগিটা পাসি চায়,1,crime
শালা কুতার বাইছা,1,crime
মিন্নি কুত্তার বাচ্চা টার পাসি চাই । ভিডিও তে স্পষ্ট বুঝা যায় মিন্নীর এর পিছনে সরাসরি হাত আছে,1,crime
তোরা কুত্তা চোদা সাম্বাদিক তার কেনো জুন করলা এখন য়েটাকি ড়িচি নাকি অন্নো কে বুজবো কিবাব্য,1,crime
হোক সে জেলা প্রশাসক ধোনের জ্বালা তো আছে নাকি!,1,crime
এই মাগির কথাগুলো শুনে আমার কাছে থাকা আরেকটা জামালপুরের মাগির ভিডিও আছে সেটাও মন চাইতাছে সবার কাছে ভাইরাল করে করে দেই,1,crime
আমার সারে আমার পাছা দিয়ে দিল আইক্কা আলা বাঁশ,1,crime
মেয়েটা।করেছে অভাবে।। আর ডি সি। লুইচচা।। মেয়েটাকে চুদেছে । চুমমা। খেয়েছে। লেওড়া। ঢুকাইছে। দুধ টিপিলো।,1,crime
তুমি কুলাংগার এর বাচ্চা কুলাঙ্গার এগুলা নিয়া এত দালালি করতেছিস কেন তুইও মনেহয় এধরনের লোক তোর ফ্যামিলির লোক জনও এরকমই হবে তা না হলে তোর এত চুলকানি কেন,1,crime
মিন্নী মাগির ফাসি চাই মিন্নী খানকি সব যানে খানকিতে খুন করাইছে খানকির ফাসি চাই মিন্নী ছিলানের বাঁচার অধিকার নাই মিন্নী খানকির কারনে আরও অনেক মেয়েরা তার সামীর সাথে এমন করবে আপনাদের কাছে অনুরোধ যে মিন্নী খানকিরবিচার করার দরকার নাই ছিলানরে সরাসরি ফাসি চাই,1,crime
মাদার ছুদ কিবুজাইলি রাবিশ,1,crime
সালিকে পুলিশ দরেনা কেন,1,crime
হায়রে ভোদার দেশ😁😁😁,1,crime
শালা লুইচ্চা,1,crime
মানসিক ভাবে কিসের অসুস্থ সব সালারা নাটক বাজ।,1,crime
লুচ্চা,1,crime
তুই মর কুলাংগার মহিলা,1,crime
মিন্নি ধ্বষন করা হক বরগুনা বাসী মিন্নি ধ্বষন করে রাস্তার পতিতা বানানো হক ফাসি দিলে হাজার মিন্নি জন্ম হবে,1,crime
বদমাইস আরও বলে তদন ত করবে পুলিশনা আমি সেলিম বলতেছি তদন তের গোসটীরমাইরে লইলাম আগে বাইনচুতের বদা আর য়ে মাগী রুমে ছিল তারে একটু জাইগা বরাবর এসিড দিলে বিচার শেষ,1,crime
আগেই বলেছিলাম মিন্নি জরিত আছে।।।শালির বাচ্চার গোপন অঙ্গে মরিচ আর লবন লাগানো দরকার।।।কুত্তার বাচ্চার জন্য রিফাত কে আজ এভাবে মরতে হলো।।।দুক্ষিত কেউ কিছু মনে করবেন না।।।,1,crime
ভুদা ফাটাইয়া এখন বেহুস হয়ে লাভ কি ভাবিলে কি হবে গো যা হবার তা হইয়া গেছে,1,crime
শালা যদি নির্দোষ না হত প্রচার না করতে বলেছে কেন,1,crime
তুমি কোন লাইনে হাটছো তোমাকেও হুগা মারা হোক সারাজীবন খালি গোপনে চুদবা এর মাশুল দিতে হবে না,1,crime
মাগি কি কয় স্যারের চুদা আবার হবে।,1,crime
চোদা মনে হয় ভালো লাগছে স্যারের এই জন্য স্যারের দোষ নাই স্যারের পেনিস টা মনে হয় বড় মাগি সালি এই পতিতাকে এক দোম ভোদার ভিতরে বাশ দেওয়া দরকার বাসটাট মাগি এই গুলোর জন্য সমাজ সব কিছুই শেষ হয়ে য়াচ্ছে ।,1,crime
শালায় লুচ্চা দেখলেই বুঝা যায়।,1,crime
আওয়ামীলীগের ঘোষ্টি রাজাকার অশিক্ষিত মুর্খ আবাল চোরের গরের চোর মাগি পতিতা হাচিনা সরকার এর কুকুর বলে কথা,1,crime
হারামজাদা ডিসিতো বহুত বড়ো একটা লুইচ্চা।,1,crime
এই মাগি কে ও ফাসি দেয়া হউক,1,crime
মাগী একটা,1,crime
পুলিশার সব মাগি চোদা মাদার চোদ,1,crime
ভাই ওই মাগির ফাঁসি চাই,1,crime
ভিডিও তে দেখা যায় ভিডিও কি বুল চিলো মাগি স্যারের দুস তাকবো কেমনে হেটা মেলাইয়া যে দিচত আগে মাগি আমার সিরিয়েল টা কয় কতো নাম্বার,1,crime
শালা কুক্তার বাচ্চার দনটা কেটে দেওয়া দরকার,1,crime
মাগি তেজ দেখিয়ে কথা বলছে এখোনা নির্লজ্জ মহিলা একে যদি স্বাস্তি না দেওয়া হয় তাহলে এরকম লুচ্চামি করে যাবে। তাইবলে ডিআইজি ধোয়া তুলসি পাতানা ওউ সোমান লুচ্চা জাতি ওর মতো চরিত্রহীন ডিআইজি চায়না লুচ্চা ডিআইজি।,1,crime
তদের দুজনকে নেংটা করে পুটকির বাড়ি দিতে হবে চিকন বেত দিয়ে আর সারা দেশে গুরাতে হবে তারপর রাস্তার মধ্যে পকাসে ফাসি দিতে হবে তানা হলে দেশে এমন ঘনটা হাজারও ঘটবে,1,crime
এই মাগির জন্য শত নারী কলংকো হয়,1,crime
এই মাগিরে দরো আর সবাই চোদো,1,crime
শালা আবার সবার সামনেই ঘুরে বেরিয়েছে,1,crime
কুলাঙ্গারের বাচ্চারে দেখ আল্লাহর বিচার একদিন হয়ে থাকে,1,crime
ডি সি ফিট লিষ্টে না থেকেও সে ডিসি মন্ত্রনালয় থেকে যে বেজম্মা কুকুর গুলো এই খবর দিয়েছে তারা খোদ হায়েনা হাসিনা কে জিজ্ঞেস করলেই তো এই উত্তর পেয়ে যায় হায়েনা প্রধানমন্ত্রীর ফিট লিষ্টে না থেকে ও দু দুবার পোন্দানমন্তী কিভাবে হয়েছে এই প্রশ্নের উত্তর মন্ত্রনালয় গুলো আত্ন জিজ্ঞাসা করলে ও পেয়ে যায় !!!,1,crime
চ্যাটের বাল তুই ডিসি কার এত সাহস হবে তোকে হুমকি দেওয়ার। মাদারির বাচ্চা।তোর বাড়িতে পতিতালয় চালু কর সরকারি অফিসে এসব করার অধিকার কে দেয় তোকে।,1,crime
মাগীটাকে মার্কেটে দেখতে চাই দাম যেনো হাতের নাগালে থাকে।,1,crime
সারের কোন দুশ থাকবে কেন চুদা দিলে তো মজা দুই জনেই পাবে এই হারাম জাদি একটা ব্যশ্যা,1,crime
নিচপাপ দুদুর বাচ্চা,1,crime
মুন্নি মাগি জড়ীত দেকেন ওরা চার পচ জন ওকে দরেনিতাছে অই মাগি সাদারন মানুষের মত হাটতাছে,1,crime
এতের সোনা কেটে দেওয়া হক,1,crime
পাগল ছাগল তুদের আর কেয়ে দেয়ে কোনো কাজ নায়,1,crime
শালা লুচ্চামি কর আবার প্রচায় না করতে অনুরোধ কর।,1,crime
তদন্ত চোদান লাগে কিতে বুঝি না। প্রমান পাইছে এখন বিচার।,1,crime
আরে ছাগলের দল শুধু মিন্নি মিন্নি করস কেন এদের বাপ মায়েরও দোষ আছে।,1,crime
এই হত্যার পিছনে মিন্নির হাত আছে ওই মাগীর ফাঁসি হওয়া উচিত,1,crime
মাগির বোদার বিতর দিয়া গরম ডিম দেয়া হোক,1,crime
এটা বাংলাদের জন্য কোন ব্যাপার না ওই লোক করতেছে অফিস সহকারির সঙ্গে আর ওর মেয়ে করবে গাড়ীর ড্রাইভারের সঙ্গে সালা একটা লুচ্ছার বাচ্চা লুচ্ছা,1,crime
লজ্জা ও করেনা বেয়াদব একটা😡😡,1,crime
হালার হালাইন,1,crime
কি বলব স্যারের কোনো দোষ নাই স্যার তো তোমাকে করছে তাই খানকী মাকি,1,crime
কুত্তার বাচ্চারা সাংবাদিকতা কর না। এই সব নিরিহ একটু লোভি এদের সাক্ষাৎ কার নিচ্ছো।যে বাবারা এই প্রতিষ্ঠান এর মালিক তাদের কে যাইয়া প্রশ্ন কর প্রশাসনের লোকদের কে জিজ্ঞাসা কর বুজমু হেডম কত।,1,crime
চোদানি মাগি তুই মরে যা। যে ভাই এই ভিডিও টা করছে তাকে ধন্যবাদ,1,crime
বেশ্যা মাগির পোলা তোর বোন হলে কি করতি?? মাগীর পোলা ভিডিও চোদাস।,1,crime
ও মাগির ফাসি দেওয়া উচিত,1,crime
এই অাফিসার কে ধরে অাইনের অাওতায় অানা হইক তারা যদি লুচ্চামি করে তা হলে জনগন কি করবে,1,crime
লুচ্চামি কইরা এখন অনুনয় বিনয় করতাছে। মামুন বাড়ির আবদার নাকি,1,crime
মেয়েটির এই ভাবে ভিডিও করা ঠিক হয়নি সব দোহতো ঐ সালা ডিসির পারলে ডিসির ভিডিও করে পচার করো সেটা তো কারন সে পুরুষ আর এটা একজন নারী তাই খুব সহজে আনেক কিছু করা জায় সাংবাদিক কত বড় হারামি মেয়েটা মুখ লুকিয়ে রিক্শায় উঠছে তাও ভিডিও করছে আরে ভাই ওতো কারো মা বা বোন পরিস্থিতির সিকার হয়ে হয়তোবা তাকে এই কাজটি করতে হয়েছে অপমান করতে হলে ডিসি কে করুন।,1,crime
বাহ সরকারি অফিস আদালত এখন পতিতালয় হয়ে গেসে তাহলে রেপ কারা করতেছে 🙄🙄,1,crime
হায়রে কুত্তা বল্লেও কুত্তার ইজ্জতে টান লাগবে 👹,1,crime
কয় দিন পরে তার মেয়ের সাথে সেক্স করব সালার পুত।,1,crime
এই শালা তোর আর কোন কাজ নাই মাদার চোদ আজাইরা পাচাল পারিস,1,crime
এই খানকির পোলারাই দেশটা শেষ করলো,1,crime
মাদারচোদেরে দেখলেই তো বুজা যায় হালায় চোর মাদারচোদ খানকির পোলা,1,crime
তুই তাড়া তারি চুই চাইট করে মর। না হলে তোর কোপালে আরো আনে দুখ আছে। বেয়াদব মহিলা সামির পায়ের জুতা কখনো খুলচোচ আর তুই লুচ্চার পায়ের জুতা মুজা খুলে দিলি।তুই খারাপ দেশের মানুষ দেখচে।তুই একটা রাস্তার রেন্ডি মাঘী।,1,crime
তাঁর শোনার মধ্যে একটি আস্তা ইট বেঁধে দুই দিন দাঁড় করিয়ে রাখা উচিত বলে আমি মনে করি । 🖕,1,crime
তোমারে এমন চুদা দেওয়া দরকার যেনো মরনের আগে আর তোমার চুদা না চায় বুদায়,1,crime
যে লুচ্চা গুলো নারীর অধিকার প্রতিষ্ঠার কথা বলে ঐ শালারা এই ডিসির মতো নারী লোভী যার কারনে টক শো টেবিল এ আর কথা বলে না,1,crime
ঘটনা যে সত্য এবং এই শালাই জরিত সেটা ওনার চেহারা বা কথা বলাতেই পরিষ্কার বুঝায়ায়।,1,crime
সারের দোষ নাই তোমার দোষ নাই তুমি বিচার চাও তাহলে দোষ কার পাসের বাড়ির জলিল কাকার নাকি মাগি বিচার চোদাও বিচার পাছার ভিতরে দিমু,1,crime
মন্নি মাগির ফাসি চাই,1,crime
চোদার সাংবাদিক,1,crime
লুচ্চার মুখে তদন্ত করতে হবে ওর লিঙ্গ টাকে তদন্ত করলে সবকিছু বের হয়ে যাবে,1,crime
মিন্নি একটা চুন্নি৷ সে নিজেও জড়িত৷।,1,crime
শালী তর বুদায় এতজালা তর সামি কি তরে চুদা দিতে পারেনা স্যারের দোষ নাই স্যারের দোষ নাতাকলে তকে চুদল কিবাবে,1,crime
এই মাগির পোলার দানা চেচে দেয়া হোক,1,crime
সালা বদমাইসকে চাকরি থেকে বরখাস্ত করে দেওয়া হউক,1,crime
মারার সময় মনে থাকে না যে আমার পরের সময় কি হবে সব গুলো কে কুত্তার মতো পারার ওচিত,1,crime
আইন কানুন জনগণের জন্য।আজ জারজদের‌ই রাজত্ব।যাদের দিয়ে জারজ জন্মায় তারাই আবার নিতির চাবি নিয়ে টানাটানি করে,1,crime
রাইট এই মাগির ফাসি চাই,1,crime
তারা তারি মর বেলাজ্জা মাগি,1,crime
গাই গরুর জখন পালের সময় হয় তখন ষাঁড় গরুর উপরে লাফিয়ে লাফিয়ে উঠে ভিডিওতে যেমনটি দেখলাম এই মাগি লাফিয়ে লাফিয়ে স্যারেকে উপবুঘ করার চেষ্টা করছে আমি তোকে বাচার উপায় বলে দিলাম আক্কাউলা বাশ বুদার বিতর ডুকিয়ে মরেজা সাতে মরিচের গুড়া দিবি 👌👈 😤😤 😷😷,1,crime
সুবোর সালা মাগি,1,crime
মাগীরে ক্রশ দেওয়া হোক সব কিছুর মূল মাগী।,1,crime
তুই মরে যা মাগি,1,crime
কোন তদন্ত করার দরকার নাই শালারে জুতার মালায় গলায় দিয়ে সেই নডিকে বিয়ে দিয়ে একসাথে থাকার ব্যাবস্তা করা হওক,1,crime
আরে ভাই মাতবর বাড়ির কুত্তা তোমার এইটা আমাদের সেই সোনার বাংলাদেশ চুতমারানীর পোলা হুগা মাইরা দেশটারে শেষ কইরা ফালাইলো ভাই ভিডিওটা দেখুন দরকার তো,1,crime
জানোয়ার এর বাইচা,1,crime
বাচার জন্য মাদারচুদ নাটক করতাছে এই টা অরি,1,crime
শালার বলদ তোদের অবিনয় তো গাজা ভোরের মতো,1,crime
এই সব কুত্তার বাচ্চারা এধরনের কাজ করার পর সমাজে বাস করে কি ভাবে মরা উচিৎ এদের ।,1,crime
কুত্তার বাচছা সত্যি কথা এখন বাহানা,1,crime
সাংবাদিকরা এত খানকির পোলা হয় কেন?,1,crime
স্যারের কোনো দোষ নাই চোদার সময় তো স্যারের কাজ থেকে ঠিকই চোদা লও। মাগিরে রাস্তায় নামানো হক সবাই মিলে ফ্রিতে চুদে দিবো,1,crime
হেতে পদদ পিয়ন মাইয়া ইগ্গোর লাই কিল্লাই জিন্দেগী গরিলি বেক্কিন কলিকাতা হারবাল অর দোষ।,1,crime
ভাই আপনাকে গালি দিয়ে মুখটা নষ্ট করব না খান্কি মাগির পোলা এখানে তুই কি দেখাইলি এখানে দেখার মত কি আছে মাদারচোদ সময়টা নষ্ট করলি,1,crime
সব শালা কে দরেন জোয়ারি এবং বদমাসি চলে এখানে,1,crime
এখানে ভাই বিরাট ঝামেলা আছে কোপানোর কিছুক্ষণ পরেই পুলিশ আসছে।এদের সবাইকে ফাঁসি দিতে হবে আর মিন্নিকে প্রকাশ্যে পাথর মেরে হত্যা না করলেই নয় কারণ এই শালিই মেইন খুনি,1,crime
এখন দেখা জায় তার মতন ভালো মানুষ নেই আবার সংবাদ সম্মেলন করে বাইনচোদের শরম নাই,1,crime
ফাঁসির আগে এদের মেরে হাত পা ফাটাই ফেলে লবণ ঝাল মাখায় রোদে শুকায় তারপর এদের ফাঁসি দিয়া ঠিক হয় কারণ এরা তো এখন আর মানুষ নয় জানোয়ার হয়ে গেছে এমন ভাবে একটা মানুষের প্রত্যাশার করছে এরা,1,crime
ঐ শালা ভিলেন,1,crime
খানকি মাগীরে ফাসি দেয়না কেনো এখনো,1,crime
মাগি বলে কি।।।।চোদা খাইতে তো মজা লাগছে।।।।আমারে একবার দেস।।।,1,crime
আমি বুঝলাম না দেশে এতো সমস্যা থাকতে মিডিয়া কেন এই বালের পিছনে পড়ে আছে🙄,1,crime
সালারা বোকা চোদা। মিন্নিরে কপাইল না কেন।,1,crime
এই সালির মাগিরেও ফাশি দেওয়া হোক,1,crime
তদন্তের মারে চুদি সালা।,1,crime
জানোয়ারের বাচ্চা জানোয়ার লুচচা,1,crime
বাইঞ্চোদ আবার ক্যামেরার সামনে কথাও বলে।লজ্জাও নাই।,1,crime
নয়নের চেয়ে শিশ্ব সন্ত্রাসী আছে ধরাছোঁয়ার বাইরে আছে আমাদের সমাজের মানুষ নয়ন থেকে নয়ন বন্ড বানাইছে মিন্নি শয়তান নষ্ট বেয়দব খারাপ মেয়ের কারনে এই টা ছেলে অকালে চলে গেলো মিন্নির চরিত্র ও পতিতা চেয়ে ও খারাপ এর ফাঁসি চাই এক নয়ন পরে কি বাংলাদেশ শান্তি আচ্ছে আসবে ও না এই শয়তানের কারনে হাজার হাজার মা বাবার বুক হালি হচ্ছে এই শয়তানের ফাঁসি মিন্নি তো ভিজা বিড়াল টাকার লোভ বেশি,1,crime
মাদারচোদের চেহারাতেও লুচ্চার ছাপ অনেক পাপ ভারী হবার কারণে প্রকাশ হয়েছে পাপ বাপকেও ছাড়েনা।,1,crime
শালা বাইনচুদ সাংবাদিক গিরী করস। মেয়েদের কে হয়রানি করছ কেন।,1,crime
খানকি চোদা খাওয়ার সময় মাথায় ছিল না তোর একটা বাচ্চা আছে,1,crime
শালা ভাদাইমা এখন কি ফেব্রুয়ারি মাস জানা নেই সেখা নেই রিপোর্টার হয়েছে,1,crime
এই জানোয়ার এখনো ডিসি থাকেন কিভাবে!,1,crime
নির্লজ্জ নিজের তদন্ত নিজেই করছে এই তদন্তের ফলাফলও যে কি হবে সেটা আমাদের জানা আছে। অরে তো সাথে সাথেই চাকরি থেকে অব্যহতি দেয়া উচিৎ ছিল। আমাদের দেশের মানুষ একজন চোর কে বিশ্বাস করে কিন্তু একজন পুলিশকে বিশ্বাস করে না আর জত নেতা পোতারা আছে সব সালাই চোর,1,crime
ভাই এই মিন্নি মাগির রিকসা ওলাদের দিয়ে আগে ওর গুদমারিয়ে গুদ ফাটিয়ে দিতে হবে তাহলে আমি খুশি হবো,1,crime
তুমি পতিতালয়ে যাও তাহলে বাচার মতো বাঁচতে পারবে। প্রতিদিন বড় বড় সাগর কলা খেতে পারবে।,1,crime
শালী আকাম করার সময় মনে থাকে নাই। তুরে জুতা দিয়া পিঠানো উচিত,1,crime
সব ছাগলের দল ফালতু,1,crime
বড দরনে লুচ্চা,1,crime
চুতমারানির পোলারা ভিডিও হইছে মিনিট হইছে মিনিট চোদাস কা,1,crime
শালি এখন কিচু বুজেনা,1,crime
কিছু করার নাই মানুষকে মারতে মনে তাকে না হারামিরা,1,crime
মাদারী তুইয় জরিতো,1,crime
সারের জুদি দোস না থাকে। তালে তোরে চুন্মা দিলো দুধ টিপলো আর বোদার বিতোরে নোক দিল কেন। আর তোর বোদা জুদি এতো চুল কাই তালে এক কাছ করতি বোদার বিরের এক এক্কা আলা বাষ ডুকিয়ে দিয়ে ডিওটিতে আসতি মাগির গরের মাগি,1,crime
বাহ কি বিশাল খবর নিয়া আইছে বাল ছিরা তাল গাছে উঠায়া দিছে সাংবাদিক ভাইয়েরা,1,crime
মাগিরে রিমান্ডে নিতে হবে,1,crime
তুই যে পতিতা প্রকাশ্যে এসে সেটাই প্রমান করলি,1,crime
আগে মনে ছিল না কিন্তু যখন একজন জ্যান্ত পুড়িয়ে মেরেছিল তখন একটুও আফসোস হয়নি এখন মর শালা,1,crime
বাটপারটার মুখের কোন কথা নাই লুচ্চা তার প্রমান সেই বুঝাচ্ছে।।।,1,crime
মাগি কি বলে রে,1,crime
খানকির পোলারে জুতা দিয়া পিডান দরকার মাদারচোদ ডিসি হইছে তো দালালী করে,1,crime
ঐ মাইয়া হইলো শয়তানের খাড়া জিলকি,1,crime
শালা কে সবার সামনে জুতা পেটা করা হোক । সাথে ঐ শালিটা কেও ।,1,crime
সব লুচ্চা বদমাইস গুলোর হাতে দেশের দায়িত্ব দিয়ে রেখেছে হা আর কি দেখা আছে বাংলাদেশ জনগণ,1,crime
সালার গরের সালারা আসামিদেরকে অন্য কারাগারে নেওয়ার খবর তারা যানে কেমনে আবালের আইন নাটক করে নাটক,1,crime
টয়লেট খাওয়া পুরুষ এখন পতিতালয়ের মালিক,1,crime
মাগি আবার বরকা পরছে 😃,1,crime
আমাকে নিজের কাছে নিজে পরিচয় দিতে লজ্জা করে যে আমরা আসলেই বাংগালি নাকি এত গুলা মানুষের সামনে কি ভাবে একটা মানুষকে দুজন মিলে এই ভাবে কোপাতে পারে কেও আসল না??? থুথু মারি এই জানোয়ার গুলা কে। আর পুলিশ এখনো কেনো মিন্নি কে ধরছে না?,1,crime
তুমি শালা সাংঘাতিক সকল সাংবাদিকদের ধর্ষণ করেছো । আগে কথা বলার ভাষা ভালো করে শিখো তারপরে সাংবাদিকতা করতে আসো।,1,crime
মাগির পাসি চাই,1,crime
ডাল কড়াইয়ে দেওয়ার আগেই ডাল পড়ে গেছে হালার।চুমাচুমিতেই ডাউল শেষ!হালার পুত সরকারি কর্মকর্তা হয়ে এইসব করে।এমন শাস্তি হওয়া উচিৎ যেন চাকরির লোভ দেখিয়ে আর কেউ অন্যের মা মেয়ে বোন স্ত্রীর সাথে এমন করতে না পারে।সংসার নষ্ট করা এইসব কুত্তার বাচ্চাদের পশ্চিমা দেশগুলোর মতো বিচার হওয়া উচিৎ লিঙ্গ হাত কেটে ফেলা ।তা তো আমাদের সরকার জীবনেও করতে পারবে না।তাইতো দেশে দিনের পর দিন এইসব জানোয়ার রূপের মানুষগুলোর জন্ম হয়।মহিলাটিকে ব্ল্যাকমেইল করা হয়েছিল বলে মনে হয় ফুল ভিডিওতে দুইটদুইটা তারিখের সিসি ক্যামেরা রেকর্ড আছে।মহিলাটিরও শাস্তি হওয়া উচিৎ।কি দরকার স্বামী সন্তান রেখে চাকরির লোভে ফাঁদে পা দেয়ার।আমার মতে এই দেশে মেয়েদের উচ্চশিক্ষায় শিক্ষিত না করা উচিৎ।মেয়েদেরকে বেশি পড়াশোনা করালে চাকরি করতে চায়।নিজের পায়ে দাড়াতে চায়।পরিবার স্বমী কি তা মনে থাকে না ওইসব জানোয়ারদের ফাঁদে পা দেয়।নিজের পায়ে দাড়াতে গিয়ে ওই জানোয়ারদের বিছানায় গিয়ে শুতে একটুও দ্বিধা বোধ করে না।আমার কথাগুলো কারো খারাপ লাগলে ক্ষমার দৃষ্টিতে দেখবেন। যদিও এটাই বাস্তব।এরকম অনেক জানোয়ারই সমাজে লুকিয়ে আছে।একজনের যদি উপযুক্ত শাস্তি হতো তাহলে এইসব পরকীয়া করার সাহস কেউ করতো না। ধন্যবাদ।,1,crime
ওই একটা কুত কুত্যার বাচ্চা,1,crime
ডিসি সাহেব চোদান কে ৷ তারে বলতে হবে কুকুর,1,crime
মিন্নির মাগীর ফাসি চাই।,1,crime
লুচ্চা লুচ্চা লুচ্চা লুচ্চা লুচ্চা লুচ্চা লুচ্চা লুচ্চা লুচ্চা লুচ্চা লুচ্চা লুচ্চা লুচ্চা লুচ্চা লুচ্চা লুচ্চা লুচ্চা লুচ্চা লুচ্চা লুচ্চা লুচ্চা লুচ্চা লুচ্চা লুচ্চা লুচ্চা লুচ্চা লুচ্চা লুচ্চা লুচ্চা লুচ্চা লুচ্চা লুচ্চা লুচ্চা লুচ্চা লুচ্চা লুচ্চা লুচ্চা লুচ্চা লুচ্চা লুচ্চা লুচ্চা লুচ্চা লুচ্চা লুচ্চা লুচ্চা লুচ্চা লুচ্চা লুচ্চা লুচ্চা লুচ্চা লুচ্চা লুচ্চা সব শালারা লুচ্চা লুচ্চা লুচ্চা লুচ্চা লুচ্চা।,1,crime
জুতা পিটা করা দরকার দেশ টা কে পতিতা বানিয়ে পেলচে এই সব কুকুর গুলি,1,crime
আজ কোথাই সেই সব পতিতা মাগি গুলো আজ পতিবাদ করেনা আজ টক সু করেনা,1,crime
কি বলবো ভাষা নেই বরগুনারবাসীদের ধিধকার জানাই ঐ জায়গার মানুষরা এত পাষান এত নির্দয় ছি ছি তোদের কি মানবতা বলতে কিছু নেই । অার মিন্নি ও তো একটা খারাপ নোংরা চরিত্রের মহিলা ওর সামনে দিয়ে রিফাতকে ধরে নিয়ে গেল ওরা এবং রিফাতকে মেরে ফেললো । অারে এই মহিলা তোর মত খারাপ নোংরা চরিত্রের মহিলার জন্য রিফাত এর মত একটা ছেলেকে নির্মম ভাবে ওরা হত্যা করলো। এই মহিলাকে পুলিশ ধরে রিমান্ড করুক অাসল সত্য ওর মুখ দিয়ে বের হবে।,1,crime
জুতা তোদের ফালতু,1,crime
হেতির চেহারা কি শরীর পেড মোডা মুটকি,1,crime
ঐ নটির কারসাজি। ঐ নটির বাংলা ধনে হবেনা।। ওকে নাইজেরিয়ায় পাঠানো হোক।।,1,crime
জুতামার কুত্তার বাচ্চারে,1,crime
আকাম চোদানের সময় সন্তান কই থাকে,1,crime
ফাটাও সালা 🤣🤣🤣🤣,1,crime
বাংলাদেশের জন সাধারণদের বোকাচুদা পাইছে নাকি সিনেমা স্টোরির মত বোঝাচ্ছে স্বামী স্ত্রী দুজন এক সঙ্গে কোথাও আশা যাওয়ার পথে হঠাৎ ই স্ত্রীর সামনে তাঁর স্বামীর উপর দুর্বৃত্তের প্রকাশ্য আক্রমণ তাঁরা যদি প্রশাসনিক কর্মকর্তারাও হয় এভাবে পারবে না চোখের সামনে স্বামী ছেলেটিকে মারতে মারতে ধাক্কাতে ধাক্কাতে টেনে হেঁচড়ে নিয়ে যাচ্ছে বউ দিব্যি নরমাল মুডে হাঁটছে বউয়ের দৌড় নাই চিৎকার নাই এমনিতেই মহিলাদের চিৎকার শুনলে জন এগিয়ে আসে যখন ক্যামেরা হতে একটু অতিক্রম করলো ছেলেটিকে নিসংশ কোপাতে শুরু করলো তখন ক্যামেরার দিকে তাকিয়ে ওদের টানছে দেখুন আরেক কুত্তারবাচ্চা কি দারুণ এক্টিং করছে বাহ কিয়া বাদ হেয় মাননীয় প্রধানমন্ত্রীর নিকট আমাদের একটাই দাবী মিন্নি সহ সবগুলো অমানুষের বাচ্চাদের প্রকাশ্য ফাঁসি দিন এরা দেশের শত্রু দশের শত্রু বাংলাদেশের প্রতিটি শহরে আনাচে কানাচে এই সকল কুকুর বিদ্যমান,1,crime
পোলাপান জন্ম দেওয়ার আগে একবার চিন্তা করবেন পোলাপানগুলা মানুষ করতে পারবেন কিনা এগুলা সব কুলাংগার এর বাচ্চা,1,crime
এই জেলা প্রশাসক এর নুনু গোড়া কেটে দেওয়া হোক,1,crime
এই মাদার চুদ বদমাশ,1,crime
আইন শ্রিংখলা বাহিনী এখন লুচ্চা বাহিনীতে পরিনীতিত হয়েছে। ইয়ে ছব মুহাব্বাত কা পেয়ারহে অর কুচ নেহি হে,1,crime
শালারা বাটপার হেডিং ও ভডিও এর কোন মিল নাই।,1,crime
বালের তদন্ত করবে শালা তোর চাকরি কিভাবে থাকে এখনো। মাদারচোদ তুই জেলে যাবি কবে,1,crime
ওই মাদারচোদ এর দৃষ্টান্ত মূলক শাস্তি দাবি করছি। দেশের মানুষের পুলিশের উপর থেকে ভরসা উঠে গেছে। এদের মতো কয়েকটা কুত্তার বাচ্চা দেরকে সঠিক সাজা দিলেই দেশে আবার প্রশাসন শ্রদ্ধা মানুষের মাঝে ফিরে আসবে,1,crime
তোমার হোগা মারা সাড়া🤣😂😂🤣,1,crime
ওরে কেউ কিছু বলে না কেনো হেকার গুরুপেরা উরে কি কিছু করছিলো না কি মেয়ে টার সাথে তো ওই কুত্তার বাচ্চায় থাকতে গিছে ছিলো,1,crime
পরিবেষটা সুন্দর না কোন হৈ চৈ আছে ডেলে দেই।নাটক বন্দ কর চোধাচুদি করা সময় বেহুস হইলা না এখন কোন দুষে এমন কর কেন ময়না কত বেডা সোনা জানি মাপ ছো তুমি জান ভাল করে,1,crime
আরে তুই তো মাগি,1,crime
খুন হবার সময় তো অনেক লোক সুটিং দেখছিল। যে যার মত পালাচ্ছে। কত নিলজ্জ ভীরু হলে এরকম থাকতে পারে। বাঙালিরা গাল মারতে জানে পর সমালোচনা করতে জানে কিন্তু প্রতিবাদ করতে জানেনা। আবার অতিরিক্ত ধার্মিকও সাজে। শালার অসভ্য একটা জাতি।,1,crime
সালার পুত মাগি বাজ,1,crime
প্রতিবন্ধী হিজরা৷ জংগী মাদারচোদ জনগন।।আমি নিজেও অন্তর্ভুক্ত।। খালি পারে ধরশন করতে।।সালা। পুরুশ হলে জন এ যথেষট।,1,crime
সবাই শুধু ডিসি সাহেবের দোষ দেখছেন আসলে তার চেয়েও যে এই খান্কি মাগির বেশি দোষ এটা আপনারা বলছেন না কেন আগে এই খান্কি মাগির শাস্তি দেয়া উচিত তারপরে ডিসির,1,crime
সালার পুতে গরে পুটকিয়া বাশ টুকানোর দরকার,1,crime
বালের অভিনয়,1,crime
রান্ডি মাগী,1,crime
সব সত্যি ঘটনা। সালারে জুতা পিঠানো করা দরকার,1,crime
রোখক যদি জানোয়ার ধরসোক হয় তা আমজনতা কি করবে এটাতো উন্নয়নের জোয়ার,1,crime
মাগী বেহুঁশের অভিনয় চুদাইছে!!! জামালপুরের কি কোন পুরুষ নাই থাকলে এ জানোয়ার এখনো বুক ফুলিয়ে চলাফেরা করে কিভাবে! ওরে গনধুলাই দে,1,crime
জারজ ডিসি,1,crime
বাইঞ্চোদের কোনো ব্যপারে কোনো রিয়েলাইজ করা যাবে,1,crime
এই শালা কুত্তার বাচ্চাকে ফাঁসি দেওয়া হোক,1,crime
জানোয়ার থাকে 😠😠😠,1,crime
মাগিটাকেও ফাসি দেওয়া হোক,1,crime
হালার পুত সোনার ভিডিও বানাইছোস কোনো কিছুর সাথে মিল নাই।,1,crime
অভিনয় করতে পারোনা কি বাল করো।।,1,crime
শালী মিথ্যাবাদি,1,crime
ওর পুটকি দি রট দে,1,crime
ঐ ডিসি হলো বড় জানোয়ার ঐ মহিলা তো হলো ওর লাল ওসার শিকার,1,crime
কুত্তার বাচ্চা পুলিশ বাংলাদেশের সবচেয়ে নিকৃষ্ট জাতি সাপ কে বিশ্বাস করা যায় কিন্তু পুলিশকে বিশ্বাস করা যায় না,1,crime
আমার বাংলা কথা বলতে হবে আগেই বলেছি ওই মাগী সব করাইসে। একজন ভালো ইস্তিরি হলে যখন তার স্বামীকে দোরে নিয়ে যাইতেসে তখন তার ভিতরে কিছুই হয় না । নাটক করছে ওই মাগী। রিমান্ডে নিয়ে জিজ্ঞাসাবাদ করে শুয়ে ওই মাগীর ভোদা র ভিতরে গরম ডিম দিলে সব ফোর ফোর করে বলবে।,1,crime
আগে এ চদানির মাগিরে আইনের আওতায় আনতে হবে।,1,crime
এখন সবাই বলে রিফাত হত্যার বিচার চাই যখন সবার সমনে রিফাত কে কোপাইতেছিলো তখন তো সব সালারা তামাশা দেকতেছিলো কই তখন তো কোন সালারা ফিরাইতে আসে নাই,1,crime
বিচার তোর পুটকি দিয়ে ঢেলে দেই,1,crime
সালা সয়তান,1,crime
তোদের মতো মাগিদের বাচার দরকার নাই সমাজ নষ্ট করচ তোরা মরি যা কুত্তার বাচ্চা,1,crime
ওয় মাগি এখনো বেচে আচে কি করে ওয় মাগির জন্য এখন আমি সব মেয়েকে ঘীনা করি,1,crime
এই সালার পুত তদেরই লোক ত তাই মিথ্যা বলে চালিয়ে দিছস,1,crime
মাদারচুদের রিমান্ডে দেওয়া দরকার অফিসসে কেনোঅফিসকে অপমান করা হল পুলিশ কোথাই।,1,crime
ছিঃ ছিঃ মিন্নি কেনও এখন মাগিরে শাস্তি দেয়না খানকিমাগি রে কুবা কুত্তার বাচ্ছা মিন্নি,1,crime
ডইনী খুনী মাগী ফাঁসি চাই,1,crime
বোকাচোদা কয় কী,1,crime
জানোয়ারের বাচ্চারা অবিনয় করে ফাসি চাই আজ আমরা অনেক খুশি হা হা হা,1,crime
আমার মনে হয় শালায় সোনা পুরাটা ঢুকায় দিছে ভিতরে তাই অজ্ঞান হয়ে গেছে,1,crime
এদের মত পুরুষ মহিলার কারনে জারজ সন্তানের অভাব হয়না,1,crime
ডিসি লুচ্চার সর্দার দালালি করবেননা।,1,crime
মাগিনা মার,1,crime
এই মাগিরে লব মরিচ দেয়ে দরকার,1,crime
মাগির পুত তোর জাতের মাইরে চুদি।তোরাই দেশটা কে শেষ করে দিলি,1,crime
ডিসির দোষ থাকবে কেনো ডিসিতো মজা দিছে তাই ডিসি ভালো ডিসির সামনে সব খুলছে আর একহন বোরকা হিজাব পরে কথা বলে এ সব নারীরা হলো বাংলা দেশের ফ্যাশেন মাগী আগে জানতাম মেয়ে রা দেহ বিক্রি করতো একহন কার মেয়ে রা দেহ বিক্রি করে ফ্যাশন করার জন্য,1,crime
এরা জানোয়ার মানুষ না,1,crime
কুত্তির ফুড়ি কাজের সময় ত জালায় আরামে এসব চিন্তা করলে না,1,crime
আরে খানকির পোলা তর মারে চুদি মেয়ের কেমেরা লাগানো যদি অপরাধ হয় তর ডিস বাপে যে চুদাচুদি করছে সেটা অপরাধ নাই,1,crime
সবাইকে কি বোকাচোদা মনে করে নাকি তারা,1,crime
কি যে লিকব আমার নিজেরই লজ্জা আসে কিন্তুু লিখতে হয় কিছু কিছু জারক সন্তান জারক মেয়েদের কাজ কাম দেখ লেখার জন্য প্রয়জন হয় ডিসির সাজা হক তার ভোগা কাইটা তার হোগাদিয়া্ দেওয়া দরকার আর মেয়েটার সোনা দিয়া লোহা গরম কইরা ডুকানের দরকার,1,crime
শালার বিরুদ্ধে দুদককে লেলিয়ে দিবো।,1,crime
ভাই একটু ও বনে নাই এসব না করে রিফাত হত্যা কারি সবার জেনো ফাসি হয় না ফাসি দিয়ে নই কুত্তার বাচ্চা রার যেনো নির্রমম ভাবে মারা হয়,1,crime
শালা এটা তোর বড় ভাই লাগে মনে হয়  যদি নুরাত সাথে নাহে তোর বোনের সাথে হয় তুই করতি?,1,crime
আজকের এই ঘটনা কি যদি কোনো সাধারণ পাবলিক অথবা মিডিয়া র কেউ করতো তখন তোদের গোয়ায় বাল গজাতো এবং তার ইজ্জত নিয়ে টানাটানি শুরু করতি হারামির বাচ্চা রা,1,crime
হায়রে সালার মানুষ তাকা দেকতেছে,1,crime
সব শালয়ই ভালা ধরা নাখাইলে,1,crime
সালার কথাবার্তার স্টাইল বেশি সুবিধার না,1,crime
নয়ন খানকির পোলা হিজলা ওই সালা হিজলা জন মিলে একজন কে মারে সে তো হিজলা সারা কিছুই না,1,crime
মাগির দালালি করার জন্য সাটিফিকেট দে,1,crime
তোরাতো খারাপ না শুধু মাগী দেহ ব্যাবসা করিস,1,crime
মিন্নিও জড়িত তার কোনো সন্দেহ নাই ওই মাগিলে আগে পাসি দেয়ার দরখার ছিলো,1,crime
মাদার সুদেরে ধইরা লিঙ্গ কাইট্টা দেন,1,crime
চোদার দেশ ধর্ষনের দেশ গুজবের দেশ লুটপাটের দেশ পাগলের দেশ যারজ সন্তানের দেশ খানকি মাগির দেশ ভাইরালের দেশ কল্লা কাটার দেশ অত্যাচারের দেশ জুলুমের দেশ বিচারহীনের দেশ কোটি কোটি টাকা গায়েবের দেশ আমাদের এই চুনার সরি সুনার বাংলাদেশ।। আমি তুমাকেই ভালবেসে চুদে যাব।,1,crime
হারামজাদা ‌তোর ফাস‌ি হওয়া উচিত,1,crime
এই মাগি বুদা কেটে ফেলা হইক আবার বলে যে ভিডিও করছে তাকে বিচার করতে হা হা হা,1,crime
সব শালা আবালচোদা লোক অভিনয় করতে পারে না আবার নাটক চুদাও হালার পুতেরা বাস্তবের সাথে সেই রকম কোন মিল নেই শালার পুতেরা টাকা দামের খানকি আইনা মিন্নির উপর সব দোষ চাপাইতাছোছ আবালের দল।,1,crime
তোরে জুতা দিয়ে পিটাব খানকি মাগি,1,crime
ভাই যতই বলিস ভিডিও মেয়েটা করুক কিংবা অন্য কৈউ করুক ভিডিওটা করার কারণে কিনতু চোর দরতে পেরেছি। ভিডিও কে করেছে না করেছে এই গুলো নিয়ে এত মাথা ব্যাথা কেন। দালালি না। এই কুওা যে খারাপ কাজের সাথে জড়িত এইটাতো পমাণতো হয়েছে। কে ভিডিও বানাইছে না খোজে তাকে কি শাস্তি দেয়া যায় সেইটা নিয়ে ভিডিও বানান। সে একজন ডি সি হয়ে এই কাজ কেমনে করে।,1,crime
শালার কোমরে শক্তি কম হ্লায় কলকাতার হারবাল খায় না কেন,1,crime
আরে বোকাসোদা আমার বালের অভিনয় করছত? বাস্তব এর কোনো মিল নেই,1,crime
হালারপুত পাঠা,1,crime
মাগি কনকার নাটক মারো,1,crime
স্যার কিছু করে নাই তো মিনিট আপনি স্যারের বিছানায় লুটু পুটু খেলছে নাকি মাগি আবার বলে বাচ্চার কেন ইচ্ছে নাই ছেলের জন্য বেছে আছে।,1,crime
মাদারচোদ শিক্ষিত ডাকাত।এই সমস্ত নটির পোলাদের জন্য বাংলাদেশের গোয়া মারা সারা।চুরির টাকা খাইতে খাইতে চেহারাটা আপেল বানাইছে।এখন চুরি বাদ দিয়া লুচ্চামি চালু করছে তা আবার সরকারি অফিসের ভিতর। না যাই হলদি মিক্স করে এক গ্লাস দুধ পান করি।,1,crime
আর এভাবে সাংবাদিক বাইঞ্জুদ গুলা একটা নিউজ নিয়ে এমন গবেষণা চালাবে লেবু চিপে তিতা করি ঠান্ডা থাকবে,1,crime
দেশের মারে তো তারায় চুদে দিছে।,1,crime
এত গুলো মানুষ বোদা চুসসে এখন দারি দারি হুম,1,crime
আসলে ওদের কিছুই হবে না কারন আমি জানি এদেশে বিচার নাই এদেশে নিরাপত্তা নাই এদেশ একটা কুত্তা চুদা খানকি চুদা বেশশার চুদা দেশ,1,crime
ভয়ে সাংবাদিকরা কথায় বলতে পারতেছে না চুতিয়া শালারে জুতা মারই,1,crime
নডি তুই অনেক দিন দরে সোদা খাচ।এর জন্য মিথ্যা বলছ।আলগা বেডার সোদা খাছ।স্বামীর হক অন্যকে দেছ।তোকে ফাঁশি দেওয়া দরকার।জাতে ভবিষ্যতে কেও এরো কোম কাম না করে।,1,crime
এই সব মাগিদের কোবানো দরকার আমার সামিকে মারব আর আমি দেখেই চলেছি ওর ফাসি হক,1,crime
মাগি জরিত আছে,1,crime
আমরা সবাই এই কুকুর গুলোকে ফাসির রশীতে জুলানো দেখতে চাই।,1,crime
মাগী একটা স্যারের দোষ বলে নাই।আকাম করলে দোষ টা কিসের সে তাই,1,crime
জানোয়ার সালারা,1,crime
এই ভাবে বোদা পাইতা দিলে সবাই করবে,1,crime
হালার নুনু কেটা ফেলা হউক,1,crime
সালার উঠেনি ঐ মহিলা টার উঠেছে৷ মহিলাটা বিছানায় যেতে ছাইলে ঐ সালা যায় নি।,1,crime
শালা ডিসি সব পুরুষ দের অপমান করছে ঠিকমত চুদতে পারিনি শালায় চাটতে পছন্দ করে।,1,crime
হাছিনারে দেখায় এই তুমার ডিজিটাল দেশ তাইনা মাগি,1,crime
মাদার চোদ পতিবাদকরার চেষ্টা কর এসব কি বানাছ,1,crime
কুত্তার বাচ্চা মাদের পুলা ওর মেয়ে থাকলে এমন বাবে চুদা দরকার ওর সামনে 🐕🐕🐕🐕🐕🐕🐶🐶,1,crime
এসব মাগীদের কে চাকরি দেয় কোন লুচ্চায়,1,crime
ডিসি একটা মাগি খানকির বাচ্চা আর মেয়েটি একটি মাগি খানকির মেয়ে ওদের জন্য সাধারণ ভাল ভদ্র ঘরের মেয়েরা চাকরি বা কাজকর্ম করতে চাইলে ও মানসম্মানের ভয়ে কিছু করতে পারে না তাই ওদেরকে চাকরিশূন্য করে কঠিন বিচার করার দরকার,1,crime
খানকিমাগি মিন্নি চুতমারানি মারাইছে ওর লাং দিয়া ছেলেডারে মিন্নি মাগির ফাসি হোক,1,crime
খানকি মাগি চুদি তোদের মত খানকি মাগিদের জন্যে আজকাল অনেক পরিবারের সুখ শান্তি নষ্ট হয়ে যায় সন্তান আছে সামি আছে তা ও তোর হয়না খানকি মাগি চুদি অফিসে আইসাও তার চুদা খাইতে হবে ঘরে যে জামাই চুদে তাতে তার আশ মিটেনা।,1,crime
পুলিশ এ কি চোখে দেখে না এতে সাক্ষ্য প্রমাণ কি আছে মাগিরে আগে ধইরা ফাঁসি দেওয়া দরকার আমরা ফাঁসি চাই ফাঁসি চাই স্বামীরে মারে কি সুন্দর করে হাটা যায় তাইলে ও সবকিছুর মূল ওই মারছে,1,crime
সবাই এই কাজ তা করা ঠিক হয় নাই আমি অনেক জাগায় চাকরির জন্য গেসি কিন্তু খারাপ কাজ ছাড়া আমার চাকরি হয় নাই মেয়ে রা না পেরে এই কাজ করে কিচু লুইচ্চা লোকের জন্য,1,crime
পুলিশ কুততার বাচ্চা তদন্ত করতেছে কে ছবিটা ভাইরাল করছে তাকে ধরার জন্য,1,crime
এই বুদার কান্নাকাটি করে লাভ নাই সব নাটক ভালো ছেলে মেয়ে জগন্মাতা দিতে পারিছ নাই খারাপ ছিলি তরা ও তাই তদের ছেলে মেয়ে এমন হয়ছে বাস আর কিছুই কইলাম না,1,crime
যারা দাড়িয়ে আছে তারা মানুষনা কুকুর,1,crime
হালার পুতেরে জুতা পিটা কর তারপর কথা হবে,1,crime
তদন্ত করে বাল ছিড়িস মাদারচোদরা দেখিসনি কতটুকু অনৈতিক কাজ করছে ইলিয়াস হোসাইন ভাই কে নিয়ে আয় দেখ কিভাবে তদন্ত করতে হয়,1,crime
রিফাত জনক যাওয়া চেষ্টা করে ছিলো মিন্নী কে নিয়ে তখন মিন্নী বেরিয়ে আসলো সেখানে গুন্ডা বাহিনী না দেখে এদিক সেদিক চুটা চুটি সুরু করল তাহার কারণ হল নয়ন বন্ড আর মিন্নী ওরা গুরুপ সবাই এক হয়ে রিফাতকে হত্যাকরেছে মিন্নী হলো আসল কুনি খাংকি,1,crime
মাগি কয় কি বিচার চায় আবার বলে স্যারের দোষ নাই।তাহলে বিচারটা করবো কার।,1,crime
আগে থেকে সন্দেহ হইছে এই মহিলা খবিশ মাগির জন্য ভালো একটা ছেলের জিবন দিতে হলো 😡এই কুওির বিচার কেনো এহনো করছে না পশাসন😞 🤬এই নটির বিচার ভালো করে করতে হবে নইলি এমন নটি আরোও জনম নিতে পারে 💆💘🤞🙄🖕🙂,1,crime
সাধনাকে বেশ্যা পাড়ার সর্দারানী আর ঐ কুলাঙ্গার কু চরিত্রের ডি সি কে সাধনার বডি গার্ড হিসেবে নিয়োগ দেয়া হোক।,1,crime
ঐ মাগীর বোদার মধ্যে হাতির সোনা দিলে ঠিক হবে মাগী মোটা সোনা খুজে ঐ মাগী এখন কোথায় ওকে আমার লাগবে,1,crime
বালের অভিনয় করছে এটা কি অভিনয় হইছে নাকি,1,crime
একে পতিতালয় ভর্তি করা হোক।,1,crime
তোরা ইতরের চেয়ে নিকৃৃস্ট মিথ্যাবাদী গীবতখোর তোরা নয়নের মত আর তোদের মা নয়নের মার মত ৷ মুখে লাগাম দিয়ে ভাল হয়ে যা গীবত জীনার চেয়ে আরও বেশী নিকৃষ্ট ৷ লানাত তোদের উপর ৷ কারন তোরা এইটা ভাবিস না নয়নের মত ক্রিমিনালের সাথে কুত্তির বাচ্চাও মিশবেনা কিন্তু নয়নের মত এদেশে হাজারো নয়নগংরা পরিবার সহ সবাইকে জিম্মি করে ভীতির উপর এক পর্জায়ে সাভাবিক ভাবে মেনে নেয় স্বামী হিসাবে আমার নিজ চোখেই বহুত উদাহরন এরকম হাজারো লাখো আছে আর তোরা বিবেকহীন হীন মনের ছোট ইতরের মন নিয়ে ভেবেছিস ৷ লানাত তেদর উপর ৷,1,crime
চোদাচুদি করার সময় খবর ছিলো না,1,crime
ভোদার পোলা তুই কি ডিচি আর সাধনার পাপের ফসল নাকি,1,crime
এই শালা ডিসিতো চুদতেই পারে না,1,crime
মাগিরে দরে ছেগা হালাও,1,crime
পৃথিবীর সবচেয়ে পর্দা সিল নারী চোদা খেয়েছে কিন্তু হিজাব খোলে নাই,1,crime
এইসব মূর্খচোদা সাংবাদিক বাদ দেও শালা চুতিয়া।,1,crime
খন্দকার সোহেল মাহামুদের কোন খতি করতেছে নাকি সে ব্যপারে লক্ষ্য রাখেন সালা লুচু,1,crime
চোদ সালাকে,1,crime
এদেরকে নিয়োগ দেয় কোন বাইনচুদ।,1,crime
চরিত্র হীন সালারে পিটায়া রিমান্ডে দিয়ে জোতার মালা দিয়া ঘুরানো হোক,1,crime
আরে মাগির পলা তোর কি বাবেরা টাকা দিছে নাকি খানকির পোলা,1,crime
আল্লায় কি শুধুই বলছে যে মেয়েরে বেশি যাবে দোজখে আরে বোন তোমার ইজ্জৎ তোমার হাতেই তুমি যদি পরদা করে হিজাব পরে পতিতা গিরি করো তাতে তো আমাদের কিছুই হবে না উলটা হাদিসের বানির সত্ততা প্রমান হবে মাত্র। অন্নো দিকে কিছু মেয়ে বলে যে মায়ের জাতি দুনিয়াতে এত কস্ট করেও কেনো যাবে দোজখে উত্তর এই ভিডিওতেই পাবেন। জাইহোক এখনকার জুগে বেশিরভাব মেয়েই খারাপ কাজ করে আর সামিকে ঠোকায় যতক্ষননা ধরা পরে। আর আবইধো মিলন এর সংি পাওয়া মেয়েদের কাছে সোজা বলে বেশিরভাগ মেয়েই এর ফাইদা লুটে। দুনিয়ায় পুরুশদের মদ্ধে লুচ্চা সুন্দর টাকা ওয়ালা দের কাছে গিয়ে মিলন করে আসে মোট মেয়েদের আর টাকার অভাব ধরিমিও বাধা ভদ্রতা ইদ্দাদির কারনে বাকি পুরুশ মেয়েদের ছোয়া পায়না। কিন্তু মেয়েরা ভালো হয় বা খারাপ হউওয়ার সুজগ পায়না বিধায় এসবে লিপ্ত হয়না। তাই বেশিরভাগ মেয়েরাই হাতে গুনা কিছু লুচ্চা সফল সিংহ পুরুষ দের চো খায় তাই খারাপ ছেলেদের সংখা মেয়েদের তুলনায় কম। জদিও এরা খারাপ বা হাল্কা ভালো মেয়েদেরকেও দেয়। তো এভাবে হিসাব টানলে বুঝাযায় মেয়েরা কেনো দোজখে বেশি যাবে।,1,crime
পুরুষ মানুষের চরিত্র ! বেশির ভাগ সময়ই এরা বাইরে থাকে কোন সময় কোথায় যায় কার সাথে কি করে বুঝা দায় শালা চরিত্রহিন,1,crime
দেশটা আজ নষ্ট হয়ে গেছে কেউ মজা নিবে নেই সুযোগটাও দেই না মানবতা নাই দেশে। মাগি যে ভিডিও করছে তার বিচার চাই টারেই সাস্তির আওতায় আনা হোক এবং যে ভিডিও করে তাদের কালো মুখ সবাইকে দেখাইছে তাকে সরকারি ভাবে পুরষ্কিত করা হোক।,1,crime
কুত্তার বাচ্চা কে এখনো স্যার বলা হচ্চে আজব,1,crime
বতর্মান সরকারের অামলে ডি সি পর্ন চবি করার জন্য ধন্যবাদ,1,crime
কিচ্ছু এইটা মিথ্যা মিন্নী একটা সয়তান নষ্ট মেয়ে তাইতো মাগির ফাঁসি চাই,1,crime
দেখলেও মনে হয় মাদারচুদেরা মত খোর।,1,crime
এই দুইটা মাইয়ারে কোলাজ কইরা তোমরা কোন টিকটিকির বাল ফালাইবা। ছাগল সাংবাদিকের দল।,1,crime
এই মাদার চোদ সাংবাদিক দের আর কোন কাম নাইতো এহন এই সব আজাইরা জিনিস লইয়া পরছে অন্য দিকে কতো মারাত্মক কিছু ঘটে সামনে আসেনা মাদারচোদের সাংবাদিকেরা মর তরা,1,crime
মাগী নাটকবাজ ভালো করে তদন্ত করে দেখলে ভালো হবে?,1,crime
দূর মাগি,1,crime
বাইনচোদ্দের চইদ্দ গুষ্টিরে আগামী দুইশ বছরের জন্য কয়লার খনিতে কাজে লাগা। আসামি সবগুলারে জন সম্মুখে ফাঁসি দে। তাইলে আর যে কুত্তা আছে ঐ গুলা শিক্ষা নিব।,1,crime
মাদার চূদেরা মূভি বানাচ কূততার দলেরা খূনির সটিক বিচারের জনন কিছূ কর,1,crime
মাগিরে জুতা মার,1,crime
নুনু কাটা হউক আর মহিলার সোনায় আগুন লাগিয়ে দেওয়া হওক তাহলে মানুষ কিছুটা হলে ও সচেতন হবে,1,crime
তোরা বাল ছিরচ,1,crime
তর৷ মারে৷ চুদি,1,crime
ডিসি র সাথে রোমে থাকা মহিলা বলছেন ডিসি স্যারের কোন দোষ নাই সব দোষ তো তার যেই হারামজাদা এই ভিডও টা আউট করছে হয়তো হতে পারে সরল বিশ্বাসে,1,crime
সালার আবাল ডিসি।,1,crime
যেইনা আমার চেহারা তার নাম আবার পেয়ারা। পেত্মী কোথাকার ডিসির বউয়ের জুতার মালা পরানো দরকার তোকে।বেশ্যা মাগি,1,crime
ওরা তো মানুষ না ওরা আওয়ামী লীগ যার বর্তমান ডিজিটাল নাম কুত্তা লীগ 😅 😅 😅,1,crime
এটা বালও বনে নাই,1,crime
মনে হলো একটা সুটিং হচ্ছে আর আবাল চোদা পাবলিক দাঁড়িয়ে দাঁড়িয়ে দেখছে।,1,crime
ওর ভোলার ভিতরে সিদ্ধ ডিম দেওয়া হোক,1,crime
নুনু কাইট্টা দেওন দরকার,1,crime
এই শালীর ফাসি চাই,1,crime
ধরে সালারে,1,crime
এই খুনের প্রধান আসামি আমার মনে হয় মিন্নী মাগী,1,crime
হান্কিরপুলারা কে জরিত আছে কি নাই সেটা পরে দেখা যেতো একটা ছেলেকে কোপাচ্ছে আর সব হিজরার দলেরা দারিয়ে দারিয়ে দেখেছে কোন দেশে আমরা বাশ করি চার পাচঁ জন লোক যদি হাতে একটি করে লাঠি নিয়ে এগিয়ে যেতো তা হলে খুনিরা ভয়ে পালিয়ে যেতো আর ছেলেটা বেচে যেতো এক মাসে শিত যায় না যারা দারিয়ে দারিয়ে দেখিছিস তদের বেলা যে এই রকম গঠনা হবে না তার কোনো গেরান্টি নাই তদের মতো মূর্খ বাংঙ্গালিদের কারণে দেশে শান্তি আসবে না তরা ভালো মন্দ বোঝিস না খালি পেট ভরে ভাত খেতে পারিস তদের কপালে কোনো দিন শান্তি নাই চোখের সামনে অন্যায়কারী খুন করে চলে যায় আর তরা হা করে জানোয়ারের মতো তাকিয়ে তাকিয়ে দেখছিস আর পিছে পিছে বড়ো বড়ো কথা বলিস সব সালারা হিজরা যারা রিফাতের খুন হওয়ার সময় দারিয়ে দেখেছিস,1,crime
মাগি মহিলা ওর ভোদায় রড ঢুকানো দরকার।,1,crime
এ হালার পুতেরা তোদের কাজ নাই তোরাই যদি হিরো হোস তাহোলে তো দেসের গোয়ামারা সারা,1,crime
ভাই এইটা আমাদের বাংলাদেশ এক জন মারচে আর একশ জন চে দেকচে কেউ প্রতিবাদ করল না শালার সবাইকে পুলিশ দরে নেওয়া উচিত,1,crime
তো কি।বালের সিসি ক্যামেরা নিয়ে এতো কথা কিসের।আকাম করছে এটা প্রকাশ করছে তো ভালোই।দুজনেই বিবাহিত।আর শালা তুই কি বলতে চাস দুইজনের সম্মতিতে হইছে বলে এটা কেউ প্রকাশ করতে পারবে না।তাইলে তো যারা প্রেম করে নোংরামি করে নিজেদের সম্মতিতে তারা বৈধ কাজ করে।শালা তুইতো একটা আসল শয়তান।,1,crime
এই শুয়োরের বাচ্চারা প্রশাসনের দেশটাকে ধ্বংস করে দিয়েছে প্রশাসনের এস আই ও সি এসপি ডিসি থেকে শুরু করে চুরিদার পর্যন্ত অপকর্মে লিপ্ত,1,crime
সালা বাঙালি এত খারাপ এত গুলো মানুষ এ মিলে চার পাচ টা ছেলেকে কিছু করতে পারেনি সব তামাসা দেখছে মিন্নিকে রিমান্ডে নিলে সব বের হবে,1,crime
স্যারের যে দোষ নাই তা আমরা জানি তুমার বোদায় যে এতো চুলকানি তা জানতাম না,1,crime
ওনি তো ছারের শিখিয়ে দেয়া কথা বলতেছে মনেহয় আরেঐ কুত্তার বাচ্চা দোষ জদি নাই থাকে সাংবাদিকের কাছে মাপ চাইলো কেনো খমা দৃস্টিতে দেখার কথা কেনো বলছে ঐ মাগি জবাব দে।,1,crime
তোর চামচামি কেউ ভাইরাল করবেনা কত পাইছো ডি সির কাছ থেকে লুচচামির বেলা মনে ছিলোনা যে কেমেরা লাগাইছে ভালো করেছে,1,crime
এ রেন্ডির মাইয়াডার যেন ফাঁসি হয় এই শালী এই ছেলেটা কে মারিয়েছে এই মেয়েটা যেন বাঁচতে নাম্বারে রিফাত খুনের মেইন আসামি হল এই মেয়েটাই,1,crime
বরো ভাই আপনি ভুদাই।,1,crime
এই মাদার চুদ কি বলিস তুই,1,crime
লুইচ্ছা সালার পুত,1,crime
শালাদের জন্য কেন কান্না করছে ওরা,1,crime
মিনির ফাঁসি চাই হায়রে চুতমারানী এই ভাবে তোর স্বামী রে মারতেছে আর তুই হেই শুদো দেখলি আমার তো কিছু লাগে না তার পর ও চোখ দিয়ে পানি বের হয়ে গেছে,1,crime
খানকির পোলা রে বাইঞ্চোদের বাচ্চার সোনা কাটা হোক 😡,1,crime
শালি টাকে জাবত জিবন দরকার মাগি,1,crime
এসব খানকির ছেলেরা সমাজাকে ধ্বংস করে ফেলেছে তুই ডিসির আত্মহত্যা করা উচিত ধর তোর বউ বাচ্চারা এগুলো দেখলো তার পরেও তোর বাঁচতে ইচ্ছে করে কিরে মাদারচোদ ডিসি ফকিন্নির বাচ্চা ডিসি তোর স্ত্রীর কি দোষ ছিল একজন স্ত্রীকে দিনের পর দিন ধোঁকা দিয়ে অন্য নারীর সাথে আকাম কুকাম করিস কুত্তার বাচ্চা মাদারচোদ তোর স্ত্রী যদি ঠিক একেইভাবে অন্যের সাথে পরকীয়া করতো তখন তোর মতো মাদারচোদ লুচ্চা বদমাশ ধর্ষকদের কেমন লাগতো শুধু এই মাদারচোদ ডিসি না এর মতো হাজারও সরকারি কর্মকর্তারা লুচ্চামি পরকীয়া করে বেড়ায় খানকি মাগীর ছেলেরা ভালো হয়ে যায়,1,crime
এই শালি একটা মাগী। ওরে আর ওর পরিবার সবাইকে পাছায় গরম ডিম দেয়া ওচিত। আর তুমি শালা কি ক্লিয়ার করবা শালা মাগীর দালাল।আমাদেরকে শিখাও তাইনা তোমার থেকে কম বোঝে জনগন সালা তুমি কি বাল বোঝ। এরকম বিডিও দিয়া মানুষকে বিভ্রান্ত করার চেষ্টা করলে তোর পাছায় গরম ডিম দিব শালা।,1,crime
ভাই আমরা জতই লিখি আসামিদের কিছু জারজ নেতা আছে তারা তাদের ছেইফ দিব আমার নেতরি আমার মা আপনে সঠিক বিচার করবেন আললায় আপার বাল করবে,1,crime
শালী বেশ্যা মাগী চুদা৷ দেওয়ার বেলায় সন্তানদের কথা মনে থাকেনা। মাগী তোর বিছার আগে হওয়া উচিৎ। সরকারের কাছে একটাই দাবী এই পতিতাকে গেপতার করে বিচারের আওতায় আনা হক।,1,crime
এই অবৈধ জারজ সন্তানের দল নয়ন বন্ড কি পাঞ্জাবি গায়ে দিছিলো?,1,crime
ডিলার চুদাও খানকি। রাতে চুদা চুদি করো আর দিনে ডিলার।,1,crime
ওই মাদারচোদকে এক্ষুনি বরখাস্ত করা হোক নাহলে তদন্ত সঠিক ভাবে করা সম্ভব হবেনা নিজের আকামের তদন্ত নিজেই করবে এটা আবার কোন ধরনের নিয়ম,1,crime
এই মাদারচোদেরা কি তদন্তের কথা বলে,1,crime
এত সুন্দর বউ রেখে কেউ কাজের মেয়ের সাথে পরোক্ষ ভাবে পতিতার সাথে কেউ ফষ্টি নষ্টি করে।লুইচ্চা বেডা একি করলো।,1,crime
স্যার আপনার নুনু গোড়াত কাটি দিলে সোজা হইলেন হয়।,1,crime
এই সব সালা দের কে জুতা পিটা করে দেশ থেকে বাহির করা হক কে কে রাজি 👿👿👿,1,crime
তুরার এডার ভিডিও নে নতুন মাদারিচুদ চ্যানেল এর টি আর পি বারাবেরলেই আর কিছু নো পর,1,crime
মাদারচোদেরা দ্বারে দ্বারে তামশা দেখছো আর প্রতিবাদ করার সাহস নাই খানকির পোলারা তোরা নাটক তারা কি কি ভাবছিস নাটক ভার্সেস এই মাদারচোদেরা শালা কাপুরুষের বাচ্চারা,1,crime
বালের আইন দিককার জানাই এমন আইনের ।।।।,1,crime
সালা মাদারের বাচ্চা কে জুতা দিয়ে পিটানো দরকার,1,crime
জানুয়ার টা আবার পদক পেয়েছিলেন এ দেশে অজথায় পদক পায় মানুষ,1,crime
ডিসির বউ একটা মাল কিরে লুচা ডিসি তোর সরম করেনা লাইভে এসে গান করস তোর বউ এখন টক বক যুবতি মেয়ে সালায় সরম নাই,1,crime
এরা উন্নত করবে দেশ যে কিনা মাগী বাজ।এদের কাছ থেকে ভালো কিছু আশা করা যায় না। এদেরকে বহিষ্কার করা উচিত এমন পদ থেকে।,1,crime
আমি এসতবদো কুওা মিননি কুওা এই কুওার অবশ্যই ফাসি চাই,1,crime
সালা এখন সাধু সাজে,1,crime
এই মিন্নি খানকি এই হত্যার মূল আসামী,1,crime
চুদে দিয়েছে ডিসি সাহেব। ক্যামারাই দরা পরেছে এটাই আমরা জানি তাই ডেসি সাহেবের ফাশি চাই কে ক্যামেরা রাখল এই সব জানতে চাই না,1,crime
যে আছে সেইটা এই শালারা জানতো না??,1,crime
চুতমারানি মাঘি চুতমারানি মাঘি আমি বলছি তোরা তো খাস আমায় তুই জামায়াতকে রে,1,crime
লুচ্চা অফিসার,1,crime
ও একটা খানকি তা না হলে জামাই থাকতে পর পুরুসের সাথে লুচ্চামি করে,1,crime
এই মাগি সবটাই ওরে দরা হোক,1,crime
ওখানে নাটক সবাই দেখছে হারে বরগুনার ছাগলের দল,1,crime
খানকির পোলায় কয় কতটুকু অনৈতিকতা হইছে মাদারচোদ পুন্দপুন্দি হইছে এরপর ও বলে কতটুকু অনৈতিকতা হইছে।🥴🤭🤣,1,crime
এর সঠিক বিচার ঢাকা শহরের সব রিক্সা ওয়ালা দিয়ে এই মাগিকে টানা বছর চু নো হোক। আর ঔই শালা ডিসিকে চাকরি চ্যুত করে সুইপার হিসেবে নিয়োগ দেয়া হোক।😠😠😠,1,crime
ওরে বলদ ছোদা,1,crime
সালা লুচ্চার বাচ্চা,1,crime
পরিস্কার ভিডিও তারপর আবার কি বালের তদন্ত,1,crime
পাগল চুদার টাইম নাই সালা,1,crime
আমরা বুঝি কোন ভিডিও আসল আর কোনটা নকল চুদা খাইতে মজা বেশি তাই সেই সময় সন্তানকে কে মনে হয়না,1,crime
ওরে বেশ্বা এখন সন্তানের কথা বলিস যখন চুদা খাস তখন তোর সন্তান কোথায় ছিল তুই যদি আমার মা হতিস তাহলে তোরে জিন্দা দাফন না করে এক ফোটা পানি ও পান করতাম না।।।।।,1,crime
তকে আমি কোন ভাষায় বলবো বুঝতে পারছি না কেমারা টা কে বসালো সেইটা নিয়ে তোর এতো মাথা ব্যথা কেন ওরা যে পাপ করলো সেইটা নিয়া তোর কোন মাথা ব্যথা দেখিনা কেন রে এর একটি প্রশ্ন কিন্তু থেকেই যায় । একটি জেলার ডিসি শাব ও নারী কল্লান সমিতির সভাপতি মাগি যদি এই ধরনের অবৈধ নোংরা কাজ করতে পারে তাহলে বাংলার সাধারণ মানুষের অবস্থান কোথায় গিয়ে দাঁড়াবে তোদের কাছে আমার প্রশ্ন,1,crime
ফালতু ভিডিও সালা মুর্খের দল,1,crime
তোদের মতো খানকির কারনে আজ যুবসমাজের মাথা উঁচু করে হাটতে পারে না।তুই যদি দোকানের সাটার টা না খুলতে তাহলে কাস্টমার আসতো না।দোকান খুলে বসলে তো কাস্টমার আসবেই। ধন্যবাদ ক্যমেরা ম্যন কে।,1,crime
ওর অন্ডকোষ কেটে দিয়া হোক,1,crime
শালীরে পাছার মধ্যে বাইড়ানির দরকার বেয়াদব নাম্বার ওয়ান।,1,crime
পতিতা,1,crime
পাবলিকের কাছে ছাইরা দেন ঔ শালা ডিসি রে দেখেন বিচার করে পাবলিক,1,crime
এটা একটা মাগি।।।,1,crime
😯 এতগুলো কুত্তার বাচ্চা 😂😂🤣🤣🤣,1,crime
ওকে চাকরি থেকে অব্যাহতি করা হোক শালা জলজ্যন্তু একটা ভিডিও কে অস্বীকার করে,1,crime
বিচার কার চাস তোদের মতো মানুষদের তো কুত্তা দিয়া খাওয়ানো দরকার,1,crime
খানকির পোলা অহন কান্দো 😂,1,crime
ডিসি ভালো করে ছুদতে পারে নাই পাওয়ার কম হারবাল খাওয়া দরকার,1,crime
হালার পোলা। তুই কুত্তা যে ভাবে লাগা সেই ভাবে লাগা ।। পিছন দিয়া চোদ। আমি সব সময় পিছনে দিয়া চোদি,1,crime
এসব কুওার বাচ্চা দের কঠিন বিচার চাই,1,crime
রিমান্ডে নিয়া গরম ডিম পাছা দিয়া ডুকালে মিনিট লাগবে সব কিছু বলতে জাস্ট মিনিট,1,crime
আচ্ছা বুজলাম না এখানে ধরা পরছে সিসিটিভির ফুটেজ তাহলে আবার তদন্ত নাম আসে কেন আর কি প্রমান চায় খানকির পুলার মিডিয়া,1,crime
লুচ্চামি করার জন্য মেয়েদের চাকরীতে রাখে। দেখা যায় লুচ্চার মত,1,crime
সব কুত্তার ফাসি চাই কোনো আপিল হবে না,1,crime
এই মেয়ে হল বড় মাগি ও খানকি,1,crime
মনে হয় কোথাও ভুল হচ্ছে কুত্তা গুলারেও একই ভাবে পুড়িয়ে মারা উচিৎ ছিলো যদিও তা ইসলামিক আইনে নিষিদ্ধ।,1,crime
এরা কি মাসুস না কি এরা আমি বুজিনা এরা আসলে কুত্তা জন্ম খানকি বাচ্চা সুকরে বচচা তো তো কোন লজ্জা নেই জারজ মাগির পুলা,1,crime
মাদারী মিথ্যা কথা বলছে চুর খানকির পোলা। 🐗🐗🐗এর বাচ্চা। ওর বউয়ের সাথে কে থাকে।,1,crime
তা শ্বশুর বাড়ির লোকের যখন এত ভয় তা এ পথে পা বাড়িয়েছিস কেন ? অসভ্য মেয়েলোক,1,crime
যে হালার ক্যাসিনো তার পুটকি দিয়া গরম রড় দেন র‍্যাব স্যার আর যারা খেলতে আইছে তাদেরকেও দেন টাকার জন্য যার মায়া নাই তাদের উচিৎ শিক্ষা দেন সেই যেই দলের হোক,1,crime
ভোদা প্রেমিক,1,crime
ফাসি দাও শালিকে,1,crime
মাগি সোনা কে বেটা দিয়ে চুদা উচিত।,1,crime
তোর মায়ের ভোদা বানাইছো,1,crime
সালাপুত,1,crime
জন্মদিনের কেক কি সুন্দর দেখা গেল বেশ্যা মাগি,1,crime
ফাসি চাই সালাগো,1,crime
মাদারচুদ তুই আর কি তদন্ত করবে,1,crime
মাগিকে ফাসি দেওয়ার দরকার,1,crime
এই বেশ্যা মাগি। অন্য জনের দোষ দেছ কেন।দরিয়ে দিয়েছে এর জন্য।অন্য জনের দোষ। তুই এক মাগি।হেতে এক বদমাইশ। তোরা দুজনকে চাকরি থেকে বাদ দেওয়া হক,1,crime
এখন আল্লাহকে ডাকো কেন?পাপ করার আগে মনে ছিলনা?আমি বিচারক হলে ফাসি না আগে ধোন গোড়া মেরে কাটতাম পরে ফাসি,1,crime
সালা তুই এক টা পাগ্ল তর মাথাই গু আর গুবর তুই ডিসির চামচা সালা বন্দ কর তর পচারুটির দুকান,1,crime
থু মারি তোরা দেশ টা কে পতিতা বানিয়ে ছাড়বি,1,crime
লুচ্চা ডিসি!😠😡,1,crime
এই সুয়োরের বাচ্চায় এক নাম্বার খানকি মাগি মর গিয়া তোর মারে চুদি,1,crime
এখন কান্না করে কি লাভ জানোয়ার তো তাদের চোখের সামনেই হইছে,1,crime
চুদ মাঘিকে দু পা তুলে,1,crime
সৌদি আরবের মতো এদেরকে ও দিবালোকে ফাসি দেয়া হোক শূয়রের বাচ্চাদের,1,crime
এই কুলাংগার হাফেজ না কি মানুষ নামের কলোংকো।এই কুলাংগার মেনে করে আমরা কোন্ দিন দুনিয়া ছারবো না এই কুলাংগারদের এখনো কেন শিরশো আদালত এই কুলাংগারদের ফাঁসি দিচ্ছে না।এদের ফাঁসি চাই।,1,crime
কমেন্ট কোরতে লজ্জা লাগে আমার খানকির বাচ্চা রা একটা তাজা প্রাণ কেড়ে নিয়েছে,1,crime
এই মাগির ফাঁসি চাই এই মাগিকে ফাঁসি না দিলে এমন আরো অনেক মায়ের কোল খালি হয়ে যাবে 😭😭😭😭😭😭😭😭,1,crime
মাগী এখন বান।ধরেছে এখন ভয়ে বোদা শুকিয়ে গেছে ওর।বোদা।আগুন দিয়ে জালিয়ে দেয়া হোক,1,crime
আবাল এটা নুস্রাত হত্তার আসামি না আগের নিউয একটা রে নুস্রাত হত্তার আসামি বানাই দিলি আবাল,1,crime
হালার পোলারা কথা বলতে পর না ।,1,crime
মিন্নীকে দেখতে তো পুরা মাগীর মত লাগে মনে হয় আবাসিকে থাকত,1,crime
সাংবাদিক কে বলছি চুর ধরা খেলে আপনাদের হাপুশ হুপুশ বেরে যায় । এর আগে আপনারা কার বাল পালান 😀😀 এখানে যে র্্যাব এসে জুয়া খেলে যায় তখন খারাপ কাজ হচ্ছে না। তখন কি ওনার রিপোর্ট তুলে দরছেন।। কথায় আছেনা হাতি খাদে পরলে চাম চিকা ও ফুটকি মাড়ে।।,1,crime
মাগের ভাই সালা জনগন চুদলে দুশ আর তুরা চুদলে নন্দঘুশ 😏,1,crime
মাগি সব মিথা বলে মাগির ফাসি চাই,1,crime
কি বলব আমাদের দেশে সরকার দেশ পরিচালনা করতে ব্যাথ। বালের সরকার।,1,crime
মিনির বোদায় পদ্মা সেতুর একটা পিলার ভরে দেওয়া হোক,1,crime
এই জায়গায় নাম বরগুনা না হয়ে হিজড়া গুনা দেওয়ার দরকার। কারণ এই বিডিও ফুটেজে দেখা যায় আশেপাশে কয়েকশত লোক ছিল। ওরা কি ছিরছে। আবাল এর আবালরা এখন বিচার চায়। এই ভাবে প্রকাশ্য খুন করে চলে আসতে পারছে তাই তাদের বিচার নয় পুরস্কার দেওয়া দরকার।,1,crime
মোটা রড আগুন দিয়ে গরম করে লাল করে উম্মে সুলতানা পপি এবং কামরুন্নাহার মনির ভোদায় ঢুকানো হোক। সিরাজউদ্দৌলা কে সবাই মিলে পুটকি,1,crime
আমরা ব্যাংকে টাকা পাঠায় কি জন্য জানেন দেশের উন্নয়নের জন্যআর তারা কি করে জানেন এরকম মেয়ে নিয়ে এস করেন শালারপুত,1,crime
সিফাত কাকু দিয়ে তাকে চোদানো দরকার। সিফাত কাকু আপনি কোথায় শব্দ বোমা মারেন না কেনো ? একটি মেয়ে পারে একটি পরিবার একটি সমাজ একটা সুন্দর দেশ কে অপমান করতে আর ধ্বংসের মুখে ঠেলে দিতে।,1,crime
ফাসি চাই সালাগর,1,crime
দেওয়ার আগে মনে ছিলো না এখন আবার বিচার চোদাও কে 😠😠,1,crime
ভাব ধরছে মাগি,1,crime
আরে ভাইয়ারা সবাই এত কথা বল্লে ডিসি কাজ করবে কেমন করে কাজ করার সময় কি এত কিছু মনে থাকে বেচারি কিছুই করেনি শুধু সেক্স করেছে এখন আবর বিচার চায় বিচার তো সেই ডিসি করবে যে তোমাকে এমন বর মিডিয়ায় দেখানো হচ্ছে তাও কি তুমার বিচার হয়নি এখন নেকামি কান্না করছে বেশ্যা মাগি,1,crime
শালি মজা নেওয়ার সময় সন্তান এর কথা মনে পড়লো না এখন বলছো স্যারের কোনো দোষ নেই কেমেরার আরালে কনডম ছাড়া জেগুলো করছো সেটা ও বলেদেও আর বল স্যারের কোনো দোষ নেই সব আমার ইচ্ছায় হোয়েছে ছুতমারানী,1,crime
শালা রে পা থেকে মাথা পর্যন্ত গু মাহায়া পেটানো উচিত,1,crime
এই মাগীর পোয়ারা এবং মাগীরা সবাই কে মেরে ফেলা দরকার,1,crime
বাংলাদেশ এই সব খান্কিদের চাকরি দেয় কে,1,crime
বোকা চোদা কয় কি,1,crime
তদন্ত তোর গোয়া দিয়া ভরা উচিত মাদারচোদ,1,crime
মজা তুমি পাইছ আমিও পাইছি শালার এত বর প্রমান তার পর আবার তদন্ত কিসের,1,crime
এই শালারে জুতা মারা দরকার,1,crime
শালা মেয়ে চুদে আবার মিথ্যা বলে,1,crime
সুমন ভাই আইন দিয়ে কিছু হবে না এর আগে তো বহুত ঘটেছে কি বিচার হয়েছে হয়নি তাদের কে পাব্লিকের হাতে উঠিয়ে দেওয়া হোক আমরা তাদের বিচার করবো প্রশাসন মাগির বাচ্চারা দেখোক কি বিচার করি,1,crime
মিন্নি কে কেন রিমান্ডে নেয়া হচ্চে না বুঝি না।এই শালি সম্পুর্ন জড়িত আর সব গুলুর প্রকাশ্যে ফাঁশি চাই,1,crime
খানকি মাগি,1,crime
মাদারচোদ কানা তুই ভিডিও বানাচ্ছিস তোর বোনকে যদি এভাবে মারতো তখন তুই বুঝতি মাদারচোদ,1,crime
গোপনীয় অফিস সহায়ক ব্যাপার টা বূঝলাম না। লুইচ্চা,1,crime
মাননীয়ো ইস্পিকার মিনিটে কিছুই হয়না বাকি মিনিটের ভিডিও কই এ তদন্ত কারে দিয়ে করাবেন ইস্পিকার সাহেব জাদের দিয়ে করাবেন তাঁরাই তো চুদির ভাই,1,crime
এই মাদারচোদ ডিসির গলায় দড়ি দিয়ে মরা উচিত এই মাদারচোদ ডিসি নিজে আত্মহত্যা করলে অনেক নারী রক্ষা পাবে একটাই না প্রকাশ হলো এর আগে হয়তো কতো মেয়ের সর্বনাশ করছে ক্ষমতার অপব্যবহার করে পাপ কখনো বাপেরও ছাড়েনারে মাদারচোদ ডিসি মাদারচোদ কে একেবারেই চাকরি থেকে বরখাস্ত করতে হবে যাতে ঢাকা শহরের রিকশা চালাতে হয় যাতে ভবিষ্যতে অন্যরাও সাবধান হয়ে যায়,1,crime
শালা তোর তো দেখি ডাইরিয়া হয়ে যাবে 🤣,1,crime
শুয়ারের বাচ্চা এখন ধরার পরে ও বড় বড় কথা,1,crime
খানকির পুলা তরে আমি আমার সামনে পাইলে মারতে মারতে মাইরা হালাইতাম খানকির পুলা মাদার চোত,1,crime
এই বেশ্যা মহিলাকে গনধর্ষণ করানো উচিৎ। আমাদের সমাজে উল্টো নিরপরাধ মহিলারা ধর্ষণের শিকার হয়!,1,crime
লুচ্চামির মত চেহারা সালা।,1,crime
শালা ব্যবসায়ী বেয়াদব। ও মিল নাই। ভন্ড কোথাকার !,1,crime
আবে মাদারচোদ রা,1,crime
হিজাবী খানকীগুলাই এগুলো বেশি করে থাকে।,1,crime
হালারে জুতার বারি দেওয়া হউক,1,crime
মাগি সেক্স করার সময় মনে ছিলোনা। তুই কার বিচার চাইছোস।যাদের কাছে বিচার চাচ্ছিস তারাও তোকে চুদে ফাটিয়ে দেবে।এটাই তোর বিচার যে ভিডিওটা করেছে জাতি তার কাছে কৃতজ্ঞ,1,crime
তোমরা এদের বাল ফালাইতে পারবানা । এই মেয় অবস্যই জরিত। সাথে স্থানীয় এমপি প্রশাসনের কর্মকর্তা । সুতরাং কিছু ই হবেনা লিখে রাখ তামার পাতে ।,1,crime
যেই গুলা কানতাসে তাদের বুদার মাজে বাশ দে সবাই,1,crime
কি কেমেরা দিয়ে ভিডিও করছে ধোন ছামা কিছুই তো দেখা গেলনা,1,crime
ওরে ধরে না কেনো মিন্নি রে মাগি,1,crime
দুর বাল,1,crime
ঐবেটাকে দেখতে লুচ্ছার মতো লাগে,1,crime
তোরা আসলে মাদার চোদের বাঁচ্চ।কারোন সব কিছু মিথ্যা কথা বলিস।তোদের কোন কাজ নাই।,1,crime
মাদারচুদরে দেখেই বুঝা যাচ্ছে ও লুচ্ছা একটা,1,crime
তুমি মজা পাইছ আমিও মজা পাইছি দুষ কেওরর নায় কেমেরার 😁😁 মাগি,1,crime
তরে আরো পাচ ঘন্টা চুদার দরকার মাগী তর ভোদার ভিতরে কত পানি আছে,1,crime
লুইচ্চা দিয়া ভরে গেছে সারা বাংলাদেশ।,1,crime
খানকি মাগি তোর চামরা কাটিয়া লবন দেওয়া ঊচিত,1,crime
মাগীর সব অভীনয়,1,crime
এই কালা জানোয়ারটাকেও এই খানে একইভাবে কোপানোর জন্য সরকারকে অনুরোধ করলাম ব,1,crime
মিনি খানকির ফাসি চাই,1,crime
আহারে ভাই টা কতো কষ্ট পেলো কতো জানুয়ারের মতো মানুষ গোলা সোটিং দেকতে ছিলো মনে হলো মেয়েটার জন্য কঠিন শাস্তি দরকার,1,crime
এই কুকুরের ফাসি হলেও সাজা কম হবে।,1,crime
সালাদের ভালো করে বিচার করা উচিৎ,1,crime
হাইওয়ান অর বাচ্চা।,1,crime
এই কুকুর বাচ্চা জুতা মারা হক,1,crime
ওই সালা সরকারি ওফিসে আকাজ করছে আরতুই কছ কিছুই বলার নেই মাদার চোদ ডিসির দালালি করছ,1,crime
বাংলাদেশের সব অফিস বা যে কোনো ক্ষেত্রে বহু জাগায় এমন লুচ্চামি চলে,1,crime
সালার কি বউ বাচ্চা নেই। এতো শরম নিয়ে কি ভাবে আবার কথা বলছে ক্যামেরার সামনে ছিঃ। তাকে আইওনের আওতায় আনা হোক,1,crime
মিন্নি মাগি আছে এদের সাথে,1,crime
ভিডিও দেখে বুঝলাম সব সময়এরা চুদাচুদি করত। আরু অনেক সুনা খাইছে সুনা খাইতে খাইতে এখন দেখলাম আর চুদতে পারেনা।,1,crime
ডিসি জেই ভাবে সামবাদিক সম্মেলন বড় বড় গলায় এখন তার মুখ কোথায় রাখবে জাস্ট নাম্বার শয়তান এই মাগি সমাজের নষ্ট বেয়াদব মাগি,1,crime
মুন্নির মতো মেয়ে সোনা দিয়ে গরম ডিম দেওয়া দরকার,1,crime
এই কুত্তার বাচ্ছা সামান্য পিয়ন কি,1,crime
সালি সোবার সময় ভাল লাগছিল আবার তুইজখন বলছ ছারের দোস্নাই তাহোলে তোর দোস,1,crime
আপনার ডিসি সাহেব এত সাধুনা যদি ভাল হত এত লুচ্চামি করত না লুচ্চামি করতে করতে একদিন তার পরিনতি এমনই হয়,1,crime
লুচ্চ সালা,1,crime
কুত্তার বাচ্চা বলে কী ওরে দরি আবার করা দরকার তাহলে হবে ওদের মতো মেয়েদের কারনে আজ নারী জাতি কে অপমান হতে হয় কুত্তার বচ্চা আবার বলে এইটার বিচার চাই,1,crime
সালা কুত্তার বাচ্চা,1,crime
শালারে নুচ্চাগো মতো দেখা যায়,1,crime
এই কুলাংগার এর বাচ্চা কে প্রকাশ্যে ফাঁসি দেওয়া উচিত চাকরির লোভ দেখিয়ে হাজার নারীকে ধর্ষণ করছে সারা বাংলাদেশে,1,crime
বাংলাদেশের মানুষ রে শালারা এখোনো আবাল ভাবে 😂😂😂,1,crime
বডিতো সেরকম মাগীর,1,crime
বেশ্যা মাগি তুই আত্মহত্যা করিস না কেন। তুই মরলে তোর সন্তানকে আল্লাহ দেখবে সেটা নিয়ে ভাবিস না।,1,crime
মাগার কেম রা ম্যান মাগীর পিছু ছাড়ে নাই,1,crime
লুচ্চামির ভিডিও হাতে পাইয়াও বলবেন তদন্ত করা লাগবে ডিসি এর পরিবারের কাউকে নিয়া আজকে জদি এসব হতো তাহোলে কি হত,1,crime
আপনারা যারা বলছেন অনুমান করা হচ্ছে মেয়েটি চাকরি বাঁচাতে জামালপুরের ডি সি র সাথে শারীরিক সম্পর্ক করেছেন। কি বুঝাতে চাইছেন বুঝলাম না। এত অন্তরঙ্গ ভাব দেখে কি তাই মনে হয় এরা কোন টাইপের পতিতা আমার জানা নেই তবে ঘটনার সঠিক তদন্তের মাধ্যমে এইসব কুলাঙ্গারদের বহিষ্কার করা হোক।,1,crime
দুই জনের সম্মতিতে সেক্স করছে যেখানে মেয়েটা নিজেই বলতেছে স্যারের কোন দোষ নাই সেখানে কুত্তার বাচ্চা সাংবাদিক গুলার এতো জ্বালা কেন শুধু সরকারি অফিস জন্য সরকারের রাইট আছে এ বিষয়ে ডিসির কাছে জবাবদিহি করার এছাড়া এটা কোন অপরাধের ভিতরে পরে না । এটা নিয়ে এতো নিউজের ছড়াছড়ির কোন মানে হয় না ডিসি এবং সাধনাকে স্বাভবিক জীবনে ফিড়িয়ে দেয়া হোক ।,1,crime
এসব কুত্তার বাচ্চা জন্য দেশ নষ্ট হচ্ছে,1,crime
কি বাল,1,crime
কারন একটাই বিওটি চুদার ফুল দুনুটারে অাগুনে পুরানু হোক,1,crime
এর সাথে চুদাচুদী করে উপরে উডছে মাগী বেইশ্যা 🤰,1,crime
মিন্নি মাগির বিচার চাই,1,crime
এখন এমন ভাব ধরছে যেন সে কোন সিনেমার পাক্কা অভি নেত্রী। মাগী তোর ফাসি চাই।,1,crime
এই মাদার তোত তুই কাদছ কেন তোর বোন কে জদি এই রকম পুরে হত্য করত তুই কি করতি সালা তোরে পরা উচিত আগে,1,crime
এই মাগী অাবার বিচার চায় কেমনে সরকারী জায়গায় নোংরামি। ডিসির বাসায় মাগীর নিজের বাসায় করতি অামাদের কোন দুঃখ থাকতো না। সরকার যেখানে সব পর্নো সাইট বন্ধ করে দিলো অার তোরা সরকারি জায়গায় পর্নো র কারখানা বানাইছিস। যে ভিডিও করেছে সে সত্য টা তুলে ধরছে। বড় পদে থাকলেই যে বড় মানুষ হওয়া জায়না তার প্রমান ভিডিও। কোটি বেকার দেশে চাকরির জন্য ঘুরছে। সে খানে তুমি নিচ তলা উপর তলা সব দিয়ে নিজে চাকরি নিয়েছো সাথে তোমার দুই অাত্মীয় কে চাকরি পাইয়ে দিয়েছো। সেই পাপের ফল এখন ডিসি অার তুমি মিয়া সাধনা খলিফা দুজন ভোগ করো।,1,crime
এই সব কুত্তার বাচ্চার জানোয়ারের বাচ্চা করে বিচি কেটে দেওয়া দরকার,1,crime
এই কুকুর বাচ্চা তোর মার সাথে করলে কি কতি কুকুর বাচ্চা ডিসি চামচা ডিসি তোরে৷ কথ৷ টাকা৷ দিছে কুকুর বাচ্চা তোর৷ বোনের চৌদ লে ভালো হতো নারে কুকুর বাচ্চা তুই কি বুজ৷ বি ডিসি কি ছোটো বাচ্চা এই কুকুর বাচ্চা লুচা ডিসি আপনরা কিছু বিসেস৷ করবে না,1,crime
খাঙ্কির পুলা তুরে সাংবাদিক বানাইছে কে তুর মা বোনকে চুদায়তে দিস ডিসিকে পতিতার বাচ্চা,1,crime
মিন্নি জরিত মেয়ে লুচচা।,1,crime
সালা তোর তদন্ত তুই করছ,1,crime
মাদারচোদে পুরা আবুল হয়ে গেছে ।,1,crime
কুত্তার বাচ্ছাকে নুনু কেটে ফেলা হউক।,1,crime
এই পতিতা বলে কি দুই লম্পটকে চাকরি থেকে বহিষ্কার করা হোক,1,crime
এটা তো প্রথমেই বুঝা গেসে । ঐ মাগীর ফাঁসি চাই ।,1,crime
তাই সি সি কেমেরার দিকে তাকিয়ে ছিল। তখন চুদা চুদি না করলে পারত।ডিসি হয়ত বেতন বারিয়ে দিবে তাই চুদা খাওয়ার জন্য করেছে।এখন ধরা খেয়েছত তাই কি করবে। কেমেরা না থাকলে হয়ত কুত্তার মত জট লেগে থাকত।,1,crime
মাগির মতো দেখতে,1,crime
যে চোদানির লইগা মাদার চোদে অসহায় ভাবে ছেলেটারে মারছে সে মাদার চোদে ত বাছতে ওপারল না। আর যে চোদানির লইগা মরল সে চোদানি যে তার প্রমিকারে বাচাইতে পারল না,1,crime
ঔ মাগি তুই এত হলি সবকিছু মূল খলনাইকা,1,crime
শালার কঠুর বিচার চাই,1,crime
খানকির পোলারে জুতা দিয়ে পেঠাও,1,crime
ভাই মাগি যে কাহিনি করেছে মরার আগেও ভুলতে পারবনা এই মাগির কথা,1,crime
সালারপুতে সোনা ঠিক নাই মনে হয়,1,crime
শুশুর বারি চিন্তা করে পতিতারা,1,crime
স্নান করে মেরে এখন কান্নার অভিনয় করে কুত্তার বাচ্চা,1,crime
মাগির পুলারে এখনো মারে না কেন,1,crime
জামাল পুর নেত্রকোনা ব্রাম্মন বাড়িয়া কুমিল্লা চাদপুর ময়মনসিংহ গাজীপুর টাঙ্গাইল সাভার বরিশাল নোয়াখালি ভোলা বড়গুনার যশোহর খুলনা বাঘের হাট নড়াইল কুষ্টিয়ার পুরুষ মহিলা ছেলে মেয়েরা জন্ম থেকেই পতিতা দেহ ব্যবসায়ী মাদকাসক্ত ও মাদক ব্যবসায়ী চোরা চালানি ও ভয়ংকর অপরাধী ! এদের মাটি ও পানির দোষ ! পৃথিবী সৃষ্টি থেকেই এরা খারাপ !,1,crime
সালাকে ফাসি দেওয়া দরকার ডিসি চোদনা,1,crime
এমন মেয়ে গুলাকে চুদন বাদে কোন কথা নাই।,1,crime
রাস্তায় কুপিয়ে মানুষ মেরে ফেলছে কেওই এগে আসতে পারেনি আর এখন সব বানচোদা রা দাও হাছা নিয়ে সটফ্লিম বানাতে পারছে ভাদারমারা রিফাত কে কুপানোর সময় যদি সবাই মলে এগে আসতো তাহলে রিফাত সুন্ত্রাসীর হাত থেকে বেছে যেতো। মানুষকে মেরে ফেলছে সন্ত্রাস আর এখন সটফ্লিম চোদাও ভাদারমার ছাওয়ালেরা।এদের সব টারে ধরে রিমানন্ডে নেওয়া দরকার।,1,crime
এই সব জানোয়ারদের দমন করতে হলে একটি স্বতন্ত্র বাহিনী গড়ে তোলা প্রয়োজন,1,crime
ছি কওা বিড়ালবাচ্চা তুই কী মানুষ না ওঅমানুষ ডিসির কে বানায়ছে।জামালপুরের ডিসি তর দোজক ঠায় পাবি না। আমার কথা কে কে মত আছেন তা বলে দেন।,1,crime
এই শালি এক্টা রেন্ডি হোটেলের মেয়ে,1,crime
নয়ন বনড এর বোনকে দিনের বেলা সকলের সামনে ল্যা‌‌ঙটা করে চুদা হোক।,1,crime
মাদার ছুদ এই কয়টার কারনে দেশ আজ কোতায় এত বাজে একজন জেলা প্রসাসক,1,crime
হায়রে বাংলাদেশের আইন এগুলো বালের আইন অন্যায় করে এখনো চাকরি থাকে কুত্তা লীগের বাচ্চার হাতে দেশ টা নষ্ট করে দিয়েছে,1,crime
ভাই।এটা ইন্ডিয়ার একটা চক্রান্ত খবর নিয়ে দেখবেন।তার ওই পদে কনো মালাউন বশে গেছে এভাবেই ওরা এক এক করে সকল পদ কেড়ে নিবে। আল্লাহ আমাদের হেফাজত করুন।,1,crime
সব খানকির পোলা রে মাইরা কুত্তা দিয়া খাওয়া নো হক,1,crime
এখানে যতটা আছে সবাই পাছা দিয়ে ঢুকাও,1,crime
সালার গলা কেটে দাও রাইট,1,crime
ডিসি চুদলে নিলা আমরা চুদলে বিলা,1,crime
এখন বেশিরভাগ সরকারি কর্মচারী কর্মকর্তারা অফিস আদালত যৌনপল্লীতে পরিণত করেছে এর দৃষ্টান্তমূলক শাস্তি দাবী করছি যাতে অন্য কোন কুলাঙ্গার এমন করার সুযোগ না পায়,1,crime
যে খানকির ছেলেরা এই রকম বাবে মারলো সেই খানকির ছেলেদের দরে যে বাবে রিফাত রে কোপাইছে সেই বাবে ওদের ও কোপানো উছিত,1,crime
মাদার চোদেরে পদতেক করাহক। আমি সরকারের কাছে অনুমেদন করছি,1,crime
সালিরে আর সালারে আগুনে পুড়ে মারা হোক !,1,crime
এগুলো হচ্ছে বিসিএস ক্যাডার । দেশের মাথা নিজের নুনু কন্ট্রোল করতে পারে না দেশ কিভাবে কন্ট্রোল করবে !!!,1,crime
হেকারদের কি পাগলা কুত্তা কামরাইছে সালার কোয়া চেছি দিলে হয় বাংলাদেশ টারে বরবাদ করি দিছে মাদার চোদেরা।,1,crime
এই শালি সামুকের মত ডিসির ধনকে হেটা দিয়ে মুরাইছে ডিসি আরাম পাইছে আর মহিলাটা টাকা বানাইছে,1,crime
শালা একটা পাগল। হ্যাক হ‌লে কি হয় সেটাও জা‌নে না। হাস্যকর অযুহাত। এরকম ব্য‌ক্তি‌দের হ‌া‌তে জেলার নিয়ন্ত্রন কতটা যৌ‌ক্তিক হ‌তে পা‌রে,1,crime
পতিতা শালি বলেকি ওর দোস নাই আকাম করার সমায় মনে ছিলো না আবার বলে আমার বাচার ইচ্ছে নাই আবার বলে ছারের দোস নাই ছারের ছোদায় খুব মজা পাইছে মনে হয় এসব মহিলাদের জনৌহি আনোদের সংসার নস্টে হয়,1,crime
মিন্নি দি এখনো ভাব চোদায়,1,crime
তদন্ত চুদাচ্ছে মাদারচোদরা শুয়ারের বাচ্চাকে জুতা মেরে বের করে দেওয়া হোক,1,crime
অামরা দেখেছি শুধু ডিসি দেখিনি ও কিছু করেনি কুলাঙ্গার ডিসি এর চাকুরি হতে বহিষ্কার করা হোক,1,crime
কারাপ মাগি,1,crime
হালার পুতের পুটকির ভিতরে মিসাইল দিয়ে উড়িয়ে দেওয়া হোক,1,crime
এই মাগিকে বরগুনার সব ছেলেরা মিলে চোদো তোমাতের কাচে দাবি,1,crime
লুইচ্চা রা যেখানে সেখানে লুইচচামী করে এবং করতেই থাকবে এদের লাজ লজ্জা বলতে কিছুই নেই।,1,crime
দুই খানকির পোলা আইচে তারা নাকি পুলিশ,1,crime
বোদা ফাটানোর সময় মনে থাকেনা এখন মইরা যাওয়ার কথা বলো কেন শালার পো শালা তোর জেই দেহটা সেক্স তো থাকবোই,1,crime
এক জনে চুদছে চুদুক নারে ভাই সমস্যা কি। চুদস কি খারাপ। এটা মজার জিনিস,1,crime
অর সোনা কেটে নেয়া হউক,1,crime
এরাই তো বিশ্ব ব্যাদব,1,crime
মাগি বলে বিছার ছায় শুনে হাসি পাইতেছে আমার খানকি মাগি রান্দি পতিতা,1,crime
মিন্নি জড়িত তা না হলে ও এত অাস্থে অাস্থে হাটে কি ভাবে অাবার তাকাইয়া ছেলে দেখে চারপাশে মিন্নির মতন খানকিরদের ফাসি চাই,1,crime
জয় বাংলা কুত্তাদের সামলা,1,crime
অফিস এখন চোদাচুদির জায়গা। বসে চুদে পার্টটাইম আর কলিগে চুদে ফুলটাইম। মাঝেমধ্যে হোটেলে নিয়াও চুদে।,1,crime
কোন বালের তদন্তের কথা বলে ভিডিও দেইখা পাবলিক পুরান কইরা ফালাইলো,1,crime
খানকি মাগী আকাম করার সময় মনে ছিলনা ছেলেমেয়ে আছে আর এখন বলে ছেলেমেয়ের জন্য বাঁচতে চায় ডিসির কোন দোষ নেই দোষ কার সেটা বলো আর এর মতো খারাপ মেয়ে বা ডিসির সরকারি চাকুরি বাতিল করা হোক তাদেরকে কঠিন সাজা দেওয়া হোক কাজের জায়গায় মাগী খানা বানিয়েছে,1,crime
তোর সেই দিনই মোরে যাওয়া ভাল ছিল খান্কি মাগি,1,crime
কোন দেশে বাস করছি আমরা !!এতো গুলো মানুষের সামনে মেরেছে ওথচো সবাই হিজড়ার মতো তাকিয়ে তাকিয়ে দেখেছে,1,crime
মাগী টাকে রিমান্ডে নিয়ে বেগুন ভড়া হোক,1,crime
সেক্স কি সরকারি ভাবে বৈধ,1,crime
মিন্নি চরিত্রহীন নষ্টা মেয়ে,1,crime
এর সোনার মধ্যা দৌরা মার।,1,crime
সালারেজুতা মারাহোক এতো সুন্দরভউথাকতে মাগিচৌদে,1,crime
তোম রা বাল ফালাবআ্ তদন্তর,1,crime
সালা বেহায়া,1,crime
সব দোশ সাধনা মাগি এতে কোন সন্দে নাই,1,crime
এই তোদের মার চুদে তুরা নাটক চুদাও তোদের মার চুদে মাদার চোদ খানকির মাগিরা তুরা এক জন নে বাশ জাই আর তুরা হরি হরি করিস তোদের মুখি লাতি মারা উচিত,1,crime
শালার ফাঁসি হওয়া উচিত,1,crime
জুতা মার খানকির পোলারে,1,crime
চুদানী মাগী তর বুরকা আর হিজাব এর তলে বেশ্যাগীরি পরে আছে তাত বোজার উপায় নাই।,1,crime
এলাকার মানুষগুলো পিসাচের আত্মা পিসাচগুলো তাকিয়ে তাকিয়ে দেখল হায়রে মানুষ।,1,crime
ধরা পড়লে হয় চোর ধরা না পড়লে মহা সাধু দেশে এমন মুখোশধারী বহু লুচ্চা বদমাশ আছে যারা ধরা না পড়ে সমাজে সাধু সেজে বসে আছে।।।,1,crime
মাদাচুদের বাচা কাহিনি চোদাও,1,crime
ঐ মাগী তুই অপেক্ষা কর তোর সব কুকর্ম ফাস হইসে ।গরম ডিম রেডি দেখি তোর ছিদ্র কত্তবড়।,1,crime
এক হাতে তালি বাজে না এখানে ওই খানকির ও দোষ আছে যত নষ্টের গোড়া ওই খানকি,1,crime
এই কুকুরের বাচ্চার বিরুদ্ধে আইনি ব্যবস্থা নেয়া হোক,1,crime
মাগির ভুদা কতো রস।,1,crime
বাংলাদেশের অধিকাংশ সরকারি কর্মচারীরা চরিত্রহীন এদের ভদ্র চেহারা আর ভদ্র আচরণ এর পেছনে লুকিয়ে থাকে এক নারী লোভী সয়তান!,1,crime
স্যারের কোন দোষ নাই কারণ চোদে আমিও মজা পাইছি।,1,crime
কি বলবো বন্ধুরা। আমিও জামালপুরে লোক। আমি বলতে চাই এই ডিসি খানকির পোলাকে জুতার মালা পড়িয়ে সারা জামালপুর ঘোরানো থোক। এদের মত মানুষের কারনে সমাজের আজ এই অবস্থা।,1,crime
আরে মাগী বল জে ছারের লগে আমারে বিয়ে দিয়ে দেন ছার ছাড়া আমি বাচুম না ছারের জন্য আমি মনের দুয়ার খুলে রেখেছি জির জির বাতাসে নিল নিল আকাশে।,1,crime
মাদারি চোদের দলেরা দাড়াই দাড়াই নাটক দেখতেছে এই খুনের পিছনে মিন্নি এক নম্বর অই মা পিছনে দিক দিয়ে যাচ্ছি আর সামনে স্বামী রে পিটাচ্ছে আসল মাদারিচোদ ওই ধরনের ব্যাশ্যা মেয়েরা পরিশেষে একটা কথাই বলি গালি দিয়ে কথা বলার জন্য সরি তবে হ্যা সকল ছেলেরা মডান মেয়েদের কাছ থেকে দূরে থাকুন সুখ শান্তি পেতে চাইলে পর্দাশীল মেয়ে বিয়ে করুন আল্লাহ সবাইকে হেফাজত করুন,1,crime
মাগীর পুতের ধন কাটার দরকার,1,crime
সালা তুর নাম্বের দে তুর সাতে কতা বলব,1,crime
সাদনার ভোদা তো এই ডিসিই ফাটিয়েছে।,1,crime
বলদ তোরে ডিসি কে বানাইলো যে বানাইছে সে আরো বড় বলদ। তুই শয়তানের চক্রে পা দিয়ে দিলি এখন তোর জায়গায় আরো বড় শয়তান বসানো হবে যা ভারত দ্বারা নিয়ন্ত্রিত অথবা তুই তাদের দ্বারা ব্ল্যাকমেইলিং হবি ছাগলের বাচ্চা ছাগল।,1,crime
ডিসি বাল করছে পুরা মিনিট দেখলাম আসল কথা হলো ডিসির তো কমড় লাড়া দিতে দেখলাম না🤔🤔,1,crime
মাদারচোদেরা খালি ভিডিওই বানাইতে পারো গিয়া বাঁচাইতে পারো না থু মুখে থু তরা মুসলমান নামে কলঙ্ক এক ভাইরে চোখের সামনে হত্যা করে আরেক ভাই ভিডিও বানায় থু তগো মুখে থু,1,crime
এই সালা লুচ্চা,1,crime
চোদন নের সময় তো মজা পাইছিলে।,1,crime
সম্পুর্ন চোদার ভিডিও এর লিংক দেন আমরা দেখে বিবেচনা করি যে আসল ঘটনা কি ভিডিও এর কোলয়টি যেন ভালো হয় আমার আবার চোখে একটু 😀,1,crime
জুয়া খারাপ জানো না মাগি রা চুদা দিয়ে আবার বলো চোদা যে খারাপ জানি না মাগি রা,1,crime
চেহারা দেখেতো ডিসি মনে হয়না। কেমন যেন গ্রাইম্মা ক্ষেত লাগছে।,1,crime
ওরে মাগির ঘরের মাগি চোদানোর সময় খেয়েল ছিল না সিসি ক্যামেরা আছে সেটা হ্যাকারা মাঝে মাঝে ভালো কাজ করে এটাই তার প্রমাণ,1,crime
অই খানে যে লোক গুলা ছিল তাদের শূয়র আর কুত্তা দিতে চোদান দরকার আর অই বেতসা পতিতা মাগির নটীর ঝি কে যে কি করতে মন চাইছে রে আল্লাহ অই মাগির ফাসি চাই অই মাগিকে মিন্নি মাগি তকে যে কি করতে ইচ্ছা করছে,1,crime
আত্মাহত্যা কর সালা,1,crime
অর বুদার মধ্যে কারেন্ট দিলে সব এমনিই বলে দিবে,1,crime
এই মিডিয়ার এই সালা দের ধুনার দরকার ভাল মত এত দিন কোথাই ছিল।,1,crime
ডিসির বাল ছিরতে পারলি না এখন মেয়ে টার পিছনে লাগছিস।।,1,crime
মাগীর সোনা পরিক্ষা করা হোক,1,crime
মাগি আকাম করার সময় তর বাচ্চা কইছিলো খান্কি,1,crime
ভাই ভালো করে তদন্ত করবে ভালো মতো চোদছেনি বাচ্চা কি হবে,1,crime
মাগি নিজে কেমরা লাগাছে,1,crime
নিজের তদন্ত নিজেয় করতে চায়। ডিসি পাগল হয়ে গেছে । শালা কে লাথি মা র,1,crime
মাগিটাকে রাস্তায় নামানো হোক মানি সুযোগ আমিও একটা পাইতাম আরকি আমার মত হাজার হাজার ছেলে গোলা একটু খুশিতে ঢেলে দিত,1,crime
কুত্তার বাচ্ছা তুই দালালি করবিনা নাইলে তুই ও বাচতে পারবিনা,1,crime
কুওার বাচ্চা পুলিশ তোদের জন্য আজ দেশের এ অবস্থা,1,crime
ভিডিও তো আর কেউ বানায় নাই এটা কলেজ সিকিউরিটি ফুটেজ কাজেই আর প্রমান লাগে না রিফাতকে গুলি বা ফাসী দিয়ে নয় সরাসরি ঐ কলেজ গেইটে এনে রাস্তায় দিনের আলোতে মৃত্যু না হওয়া পর্যনত জন মিলে কুপিয়ে যখম করা আর মিননির কথা কি বলবো ওতো মেয়েদের সারিতেই পড়ে না যারা পতিতাবৃত্তি করে ওদের ও একটা সমমান আছে মিননি খানকিরতো তাও নাই ওকে ও প্রকাশ্যে পাঠা বলী দেয়া হবে আসল বিচার দিখ মিননির জন্ম দাতা পিতা মাতাকে যারা মেয়ে নিয়ে ব্যাবসা করে এটা ব্যাবসার মতোই শুধু জন্ম দিলে কর্তব্য শেষ হয়না মেয়ের বেহায়াপনা ও নজর রাখতে হয় বাংলার কোটি মানুষের থুথু ঐ কুলাংগার মাতা পিতার উপর। তোরা ভিডিওটা ভালো করে চোখ দিয়ে দেখিস।,1,crime
খানকির ছেলে এসপ নাকরলে হইছে কিভাবে বাইচত,1,crime
ওই মাগির ফাসি চাই,1,crime
খানকির পোলাদের ফাঁশি চাই,1,crime
এই কুত্তার বাচ্চাকে এই লুচ্চাকে চাকরি থেকে লাথি মেরে বের করে দেয়া দরকার। আর জনগনের সামনে জুতা মারা হোক।,1,crime
শালারে জুতা পিটা করা দরকার। নারী সহকর্মীর নাম সানজিদা ইয়াছমিন সাধনা। ঐ মেয়ের ছবি ভাইরাল করা হোক।,1,crime
এইশালা ওছিরে পবলিকের হাতে ছেড়ে দেওয়া পাবলিক ওরে চুদে গওয়া ফাঠাক শালা মাদার চোদ,1,crime
সারে পেন কুলে চুদলে কুন দুষ নাই ।পাবলিকে পেন কুলে চুদলে দুষ কেন জাতি জানতে চায়,1,crime
সালারা দেখ ডিসি সাইবের চেয়ে মেয়েটার দরকার বেশি ছিল,1,crime
হেতের কি সরম লাগের না লুইচ্ছা,1,crime
এই মিন্না খানকি মাগি জরিতো পুলিশ ভাইরা কি করে ওরে এখনো ধরে না কেনো মিন্নির ছামায় গরম ডিম ডুকাও সব বলে দেবে,1,crime
আমার বাল আসল ঘঠনা জানস বেটা?,1,crime
লজ্জা লাগে এতো লোক দের সামনে মারলো আর সবাই মজা নিলো। সবাই এগিয়ে আসলে একটা মা এর কোল খালি হতো না। আরএ কুওা গুলো তোর আপনজন দের তো এমন হতে পারে। মনে রাখতে হবে কেউ বিপদে পরলে আমি এগোলে আমার বিপদে আরাক জন কে পাবো।,1,crime
সালারে জুতা পেটা করা দরকার,1,crime
এই শুয়োরের বাচ্চা দের সরাসরি ক্রসফায়ার দিন । কোন জবানবন্দি ছাড়া,1,crime
দেশে এখন দুই ধরনের দালাল 👉পাকিস্তানের দালাল 👉ভারতের দালাল আর আমরা বাকিরা সবাই ছাগল,1,crime
খানকির পুলা তুই অগলেগা ভিডিও বানাস ওরা অমানুস তুই বর খানকির পুলা অমানুস,1,crime
খানকির পোলা কচু গাছের সাথে পাশি দিয়া মর।। তোর যদি লজ্জা থাকে তাহলে এই মুখ আর কাউকে দেখাস না।।লজ্জা বলতে যদি তোর কাছে কিছু থেকে থাকে তাহলে তুই অবশ্যই মরবি শালা।। শালা বলে কিনা আমি বিষয় টা খতিয়ে দেখছি।চুরি চুরি আবার শিনা চুরি।।,1,crime
বোকাচোদা,1,crime
হালার পাওয়ার নাই।ঠিক মত খেচতেও পারলো না,1,crime
সালির মাগি আবার বিচার চাই খানকি তুর ছেলেকে লোকে বলবে মাগির পুত 😄😄😄😄,1,crime
মাগীরে সরকারি হিসেবে ঘোষণা করা হোক। সবাই মন মতো চুদবে। কোন টাকা দেওয়া লাগবে না।,1,crime
কুত্তার বাচ্চা সন্তানের কথা আগে খেয়াল ছিলোনা ! ভাষা খারাপ করার জন্য সকলের নিকট আমি দুঃখিত!,1,crime
দেশে সবচেয়ে বড়ো শয়তান হচ্ছে এই শালা ঘুষখোর চোরের মতো লোকেরা,1,crime
একদম স্পষ্ট বোঝা গেল মিন্নির হাত আছে এই হত্যা কান্ডে মাগি পিছনে পিছনে আস্তেধীরে যাচ্ছে আর ওখানে গিয়ে বাচানোর নাটক করছে,1,crime
এখন কাঁদছিস কেন রে বেশ্যার বাচ্চারা খুন করবি আর তোদের মায়ের গ্যারে ভরে দিয়েছে খুন তোদের কে দিয়ে তোদের মাকে চুদিয়ে নেওয়া উচিত খাংগির বাচ্চারা এবার ফাঁসিতে ঝুলেক,1,crime
শালি রে ফাঁশি দেয় নাকা,1,crime
আমি শুধু মিন্নি মাগির ফাসি চাই এই খানকি মাগি মিন্নি সব কিছুই জানে এগুলো মিন্নি মাগির বুদ্ধি ভাই আপনার কাছে আমার অনুরোধ এই মিন্নি মাগির বিরুদ্ধে আমাদের মতামত ওনুযায়ি একটা ভিডিও বানান প্লিজ প্লিজ প্লিজ,1,crime
হ্যাকাররা হ্যাক করে তার যৌন উত্তেজনা বাড়িয়ে দিয়েছে তাই বাদ্য হয়ে সেক্স করলো এতে তার কোন দুষ নাই।,1,crime
সবাই ফাঁসি ফাঁসি বলে চিল্লাচ্ছে।ফাঁসি কি তোর মার হুগা থেকে বের হয়?যেভাবে মারসে সেভাবে কোপ দিয়ে মার চুদান্না পোলাগুলারে।,1,crime
বাংলার বোকাচোদা ভাই ও বোনেরা কি বুঝলেন কি হইলো এইভা,1,crime
দূর বাল এটা একটা কাহিনী হল,1,crime
দেখতেই তো লুচ্চা লুচ্চা ওরে জদি ফেক আইডি ভয় দেখায় তাহলে ওরমো কি ওখানে দেখতে জিন ছিলো শলা লুচ্চার দলেরা ধংশ করে দিলো দেশ ওজাতিকে শুধু খবর না দেখিয়ে ইটবেধে লোকসমাজে ঘুরানো হোক এবং কঠিন বিচার করা হোক,1,crime
ভাই এসব পুরুনো নিয়োচ দিয়ে কোন লাপ নেই সালি মিন্নি কেন রিপাতের বাইকে চড়ে জাইনি চলে গেলে তো রিপাত শরিপ বেচে জেত এই ডাইনি আগে তেকে সব টিক করে রেকেছে মিন্নি হানকি রুপ দেখিয়ে ছেলেদের পাগল বানাই আমি মনে করি এর ফাসি হওয়া অতি জরুরি,1,crime
বেইশ্যার পোলা বাস্টার্ড তোর মা বোন কে তোর কান্দে নিয়া ডিসি কে দিয়া চুদাইয়া ভূদার জ্বালা মিটা রেন্ডির বাচ্ছা এই কানে তোর মারে চুদে সুক দিছে সেইটা দেখাইলি নাকি বাস্টার্ড। 😡😡😡,1,crime
এসব কুত্তার বাচ্চাদের কেন এখনও চাকরিতে বহাল রাখছে,1,crime
তুই মরবি কবে সালি,1,crime
লোচ্চার ঘরের লোচ্চা। ফাঁদের ডি সি কুত্তা শয়তান লুচ্চা জানোয়ার। এই ডিসি লুচ্চার পুরুষ অংগ কেটে দেওয়া হক।আমার কি তোমরা এক মত।,1,crime
আর তদন্ত করে লাভ কি উত্তর বাচ্চারে জুতা দিয়ে পিটান এ কুত্তার বাচ্চা মেয়ে মানুষকে হয়রানি করে তারা আবার কিসের দেশ চালাইব বাইরাইয়া দেশ থেকে বের করো নি কুত্তার বাচ্চাদেরকে,1,crime
স্যারের কোন দোষ নাই কারন স্যার খুব ভালো চোদন দিছে,1,crime
মাগি গুদের ভিতর গরম ডিম দে। সব বেরিয়ে যাবে।,1,crime
শালা খবিশের বাচ্চা,1,crime
আল্লাহরে ডাকো এখন শালা বানচোদের দলেরা। নুসরাত কে কেমনে মারছিলি মনে নাই?,1,crime
বালে গান,1,crime
এই সুওরের বাচ্চা ওসিকে সিরাজের সাথে জ্বালানো হউক!!! যদি দেশে আইন থাকে!,1,crime
শালা সাংবা দিক গরিবে খবর নেয় বেশি,1,crime
চুদার সময় ধরা খেলেন ডিসি। চুদা আর হল না আফসোস,1,crime
চোদা খাওয়া চেহেরা মাগির বাঁশ ঢুকাতে হবে এই সব ডিসি দেশের সর্বনাশ করবে এর চাকরী থেকে বাদ দিয়া হোক এবং ব্যাংক জবদো করা হোক,1,crime
সালায় একটা লুইচা পাবলিক কি বোকা কছু বোজে না।,1,crime
শুওরের বাচ্চা,1,crime
ডিসি জানে এই বালের দেশে কিছুই হবেনা তার,1,crime
তোর মত এরকম মাল আমার দরকার ছিলো।আহ কি ভাবে তারাহুরা কররো।আমি দেখেছি আর ভাবছি তুই যদি আমার হইতি।তোর পিছ দিয়ে দিতাম।,1,crime
দুর মাদারি ভুল নিউজ দেস,1,crime
মাগী কে ফাঁসি দেয়া হক,1,crime
নারী পুরুষের সমান অধিকার যারা চায় একটারও জন্মের ঠিক নাই সব গুলা জারুজ হারামজাদা,1,crime
ভিডিওতে তো খুব মজাই নিচ্ছিলেন এখন ধরা খেয়ে সন্তানের কথা মনে হলো!!আসলে এদের দোষ দিয়ে কি হবে ওদের স্যার তো নিদোর্ষ!!!হারামির জাত,1,crime
তোর মাকে চুদি তুই ভিডিও কেটেছিস কেনো,1,crime
খানকি মাগি,1,crime
মালটা ত ভালো আছে স্যার কুওার জমা পাইছে,1,crime
তার পর মূল অপরাধ শিকার করতে রাজি নয় মাগি,1,crime
এই মাগির হাত আচে,1,crime
ধিক্কার জানাই ঐসব জানোয়ারদের যারা রিফাত কে নির্মম ভাবে খুন করেছে। খুনি দের ফাশির আশা করছি আর হ্যা মিন্নী তুমি রেডি হয়ে থাকো মনে করনা অভিনয় করে ছার পেয়ে যাবা,1,crime
সরকার কি বাল করবে আমরা তা জানি,1,crime
মাগির একটিং নায়িকারেও হার মানাইবো।,1,crime
এইসব ছোট লোকের বাচ্চা মেয়েদেরকে জুতাপিটা করা উচিত চাকরির ধান্দায় আর কত নিচে নামবে এরা,1,crime
তবে আমি এতটুকু  বুঝতে পারলাম যে বরগুনার মানুষগুলো হিজড়া।,1,crime
তারকাচে চুদাচুদীভালো লাগে,1,crime
এই নোংরা মেয়ে গুলি কে উপযুক্ত শাস্তি দেয়া হোক ওরা তো বেশসা ।,1,crime
মিন্নি খানকির সব দোষ,1,crime
বাহ সুদির ভাই বাহ। তোরা পারিস মাদারসোদ। কোথায় মেয়েটার বিষয় হাইড করবি না তোরা উল্টা আরও দেখিয়ে দিচ্ছিস। যদি বাপের বেটা হয়ে থাকিস এমন ভাবে নিউজ কর যাতে ঐরকম আর কোন ডিসি করতে না পারে এবং ঐ ডিসির পক্ষে ন্যায় বিচার করে দেখা। তাকে তার শাস্তির ফল ভোগ করতে দে,1,crime
আহারে কি ভাবে মারল ছেলেটাকে একটু দয়া মায়া করলনা আর এইই ভাগী বিন্নি এই মাগির সবদোষ এই মাগী জরিত আছে ওদের সাথে 😂😂😂 আর পারছিনা আমি কান্না চলে আসল ভিডিও দেখে,1,crime
সালারত জন্ম দোষ আছে,1,crime
চোদা দেওনের সময় এ মান ইজ্জতের কথা মনেছিলো না মাগি,1,crime
নয়ন ভন্ড কুত্তালীগ করে মনে হয়,1,crime
লুচ্চা সালার পুত,1,crime
এইটাইপ মাগিরা কিভাবে সরকারি চাকরি পায়,1,crime
এই পতিতা এরকম কত পুরুষের চরিত্র নষ্ট করেছে আল্লাহ পাক ভালো জানেন।,1,crime
কিরে ভাই তর একটা দিয়ে চলে না দুইটা লাগে নাকি একটাই তো লোড নিতে পারবি না শালা আবার লুচ্চামি করছচ,1,crime
মাগির মাগি মরে যাসনা কেন,1,crime
মিন্নি তোমি কার আকাশে উড়ো সেই আকাশ কি ব্যাস্শা খানার চেয়ে বড়,1,crime
শুয়োরের বাচ্চার কি মেয়ে আছে থাকলে জামালপুর বাসি চুদার জন্য তৈরি হও,1,crime
ডি সি সাহেব ছেলে ভাল। মাজে মাজে একটু শরীল টা মেসেজ করতে হয়।না করলে কাজে মন বসে না। শরীল মেজ মেজ করে। ঐ মাগি ওমজা পাইছেন।ডিসি সাবের কাছে যেয়ে।,1,crime
নাটক করতে তো ভালোই পারোস তখন তোরা কোথায় ছিলি যখন ওরা সবাই রিফাত কে মারলো নাটক চুদাও না,1,crime
মিনিন হচেছ বহু রুপি পুরুস ভোগ মেয়ে । মিনিন নাটকে এ সব হয়েছ। উপর দিকে হাত বেদে পাছার ফলায় কড়া মাইর হবে তাহলে সব বেরিয়ে আসবে। সতি্,1,crime
জুতা মার শালা কে,1,crime
সালার পুট্কি দিয়ে প্রএিদিন এক কেইস গরম ডিম দেওয়া হোক,1,crime
এরকম বাংলাদেশের ভিতরে টা জেলার পুলিশ সুপার শপটির লুচ্চা নাম্বার ওয়ান কারণ আমি থানার অনেক কাছে ছোট থেকে বড় হয়েছি পুলিশদের নেচার যে কত খারাপ তা আমি জানি,1,crime
এই মাগি তুই হলি একটা 🤬🤬🤬🤬🤬🤬,1,crime
সালার পুত মিথ্যা কথা বলোস কেন। মাতার চুল কাটা বিডিওতে লোকটা চুল কাটা সেম মানুষকে বেকিব বানাস।,1,crime
চোরা মাগির পুতেরা।তোদের জন্য দেশটা ধংসের পথে।,1,crime
মাগীর বাচ্চা মাগী যখন চুদাচুদি করলি তখন সন্তানদের কথা মনে ছিলো নাহ তোদের মত বেহাইয়া খানকিদের কারণেই অন্য মেয়েরা দিন দিন ধর্ষণ হচ্ছে! এহ হিজাব লাগাইছে আবার এই যুগের শ্রেষ্ঠ বেশ্যা তুই মাগী 🤣😂😜😜😜😜😜😀😀😀,1,crime
এই সালা লুচ্চার নুনু কেটে দেওয়া হোক। কে কে একমত আছেন,1,crime
তুই লুইচ্চা বদমাইশ,1,crime
খানকিমাগী তুই মরে যা। ভিডিও কে করলো এটার বিচার চায়। শুয়োরবাচ্চা মাগী।,1,crime
ভাই এই কুত্তার বাচ্চাদের জন্য তোর খারাপ লাগতাছে।তোর বোনের সাথে যদি করতো তাহলে নিচ্চোই তোর কাছে খারাপ লাগতো না। তাই না ভাই কিছু মনে করিস না তুই বল্লাম,1,crime
খানকি মাগি তর কয় পোলার সোনা তর হোগার বিতর ডোকাতে চাস মাগি তর হোগা খুইলা দিলেও ত কে সেপ ফালাবে না সিনাল মাগি চোতমারানি তর মা বাবা কেমন সিলো তর মতো একটা মাগি জরমো দিসে,1,crime
মিন্নি বুদার বিতরে এসিট মারার এর বেশি বিগার চুদার আমার কাছে আয় দেখ কত বিগার আছে তর মিন্নি,1,crime
কুত্তার বাচ্চারা ক্ষমতা পেলে পাগল হয়ে যায়।।।,1,crime
এই শালার বেটারা এই শালীর বেটিরা সবকয়টা মাদারচোদ এগুলারে ল্যাংটা কইরা জুতা দিয়ে পেটানো দরকার শালার পুতেরা,1,crime
সালা কুতা লিগ পুলিশ,1,crime
ওর কোন মাফ নাই। শালার লুচ্চা,1,crime
বাল ফালাইবো সরকার দুইদিন পর সব ঠিক ক হয়ে যাবে।,1,crime
লুইচ্চা নাম্বার ওয়ান এরকম কত যে চলতেছে সেটার খোঁজ তো রাখেন না,1,crime
দেখতে ডাকাতের মত,1,crime
রিফাত হত্তায় মিন্নি সহ সব পশুকে কুপিয়ে কুপিয়ে মারার শাস্তি চাই । দিবালকে ওদেরকে ওদের মা বাবার সামনে কুপিয়ে মারা হক।।,1,crime
এই মাগি অনেক। বার ডিসি সাথে চোদা চোদা করছে। ।। আমি মনে করি সরকারের। উচিত। হবে পতেক থানায় পতেক জেলায়। সব ডিসি ওসি এস পি আরো বরো বরো করমো কোতা দের। কোঠোর নজোর দারি আনতে হবে ।।।,1,crime
সবাই মিন্নি রিফাত শুধু এদেরকে দুষ দিচ্ছেন। আমি মনে করি সবচেয়ে দুষি এরা এখানে যে কম না হলেও কাপুরুষ দাড়িয়ে মজা দেখতেছে হিজড়া এদের আগে বিচার হওয়া দরকার।,1,crime
এই কুক্তিদের কে গ্রেফতার করে নিয়ে যান ছি ছি ছি ছি গরম ডিম দেন সব বাহির হয়ে চলে আসবে।,1,crime
লুচ্চা মাগীরপুত,1,crime
মাগী বাজি করে আবার বিচার ও চাও😡 বিচার তো তোমার হওয়া উচিত,1,crime
কুকুরের বউয়েরা অনেক সুন্দরী হয় তুর লজ্জা থাকা উচিত শালা বদমাইশ,1,crime
মিন্নি মাগির ফাঁসি চাই,1,crime
এত পাসন মিননি নিজের সামিরে প্রেকির হাতে কেটে দিলো মাগিরে পাসি দেউ,1,crime
চুদির ভাই।।।হেহেহেহেহেহেহেহ,1,crime
এটা ভুল।কিচ্ছা সব দোস মেয়ে টার ওএকটা খানকি মাগি ওর জন্য আমরা মেয়েরা লজ্জা বোধ করি।ওর মতো মেয়েকে বেঁচে থাকার কোনও অধিকার নেই।ওর জন্য দুটি মায়ের বুক খালি।সব ওর নাটক।ওর ফাঁসি হওয়া উচিত ।,1,crime
বাকী কুক্তাদের তাড়াতাড়ি ফাঁসি চাই,1,crime
রিফাত ফরাজির ফাঁসি চাই এই কুলাংগার মায়ের কুলাংগার সন্তান কুখ্যাত খুনি এবং মিন্নি ডাইনি সহ মিন্নি হলো সমাজের কাল সাপ,1,crime
শালাকে ধন কাটেন এটাই এর শাসতি বলব,1,crime
ওই চুতমারানি মাগীকে ফাঁসি দেওয়া হোক,1,crime
চুদে চুদে বুনি টিপে ভোদা চেটে চেটে ফাটিয়ে ফেলেছে হায় হায় কয় কি,1,crime
সালারে ফাসি হতে হবে না হলে কুত্তা দিয়ে চোদা দিতে হবে,1,crime
বরগুনার সবায় মনে হয় হিজরা সবার সামনে কুপাই তেছে ওরা দারাইয়া দারাইয়া দেকতেছে,1,crime
শালা মীনির দালাল,1,crime
এক বুড়া শয়তানের জন্য কতটা লোক মারা যাচ্ছে,1,crime
মহিলা মানুষ চাকরি করা আমি মনে করি মহিলা সামি রাখিও চোদা খাই চাকরি খেথরে,1,crime
হায়রে দুনিয়ার মানুষ একটা মানুষকে এভাবে এতো মানুষের সামনে নির্সংশ ভাবে কোপাচ্ছে সবাই তাকিয়ে দেখছে যেনো কোন মুভির শুটিং চলছে এখানে। ধিক্কার জানাই তাদের এই দারিয়ে থাকা পুরুষগুলোকে। আর ঐ মিন্নি নামক ছলনাময়ী একটা বিশোধর সাপিনীকে যেনো ফাঁসি দেওয়া হয়। ঐ জানোয়ার মেয়েটা এখানে প্রধান খুনি🗡🔪। 😡😡😡,1,crime
এই হারামির বাচ্ছার জন্য কোন কষ্ট লাগে না কারণ এর চাইতে হাজার গুন চিৎকার করছিল আমার বোন নুসরাত তার পরেও ওকে পুড়িয়ে মারা হয়েছে এই হারামির বাচ্ছাদের খুব তাড়াতাড়ি ফাঁসি চাই,1,crime
এই খানকির পোলার পুটকির ভিতরে গরম রড ডুকিয়ে দেওয়া উচিত এই বেশ্যা মাগির পেট থেকে জন্মানো ছেলেদের কারনে পুলিশদের সবাই খারাপ দৃষ্টিতে দেখে।,1,crime
মুক্তিযুদ্ধের সময় এই শালারা ছিলো রাজা কার আর এখন মুক্তি যোদ্দা সাজে।,1,crime
জানোয়ার বাচ্চাদের ফাঁসি তাড়াতাড়ি দেওয়া হোক,1,crime
মুক্তি যোদ্ধা দে রার নাম ভাঙিয়ে এই রাজাকারের বাচ্চারা খাচ্ছে । পুলিশ এক নাম্বার কুকুরের বাচ্চা,1,crime
মালের স্বাদ না পেয়ে বেহুস। হায় রে মাল,1,crime
গরু ছাগল হ বাল আছে তার চাঁদে গরু বাচ্চা গরু,1,crime
খানকির পোলা রিফাতরে ডাইরেক কুপা কুওার বাচচারে কোন আইনের দরকার নাই ডাইরেক কোপ ।শুয়ারের বাচচা ।,1,crime
শুয়োরের বাচ্চা দের ফাসির চাই,1,crime
খানকি পোলা কই কতটুকু খারাপ করছে,1,crime
আপু অনেক পরেজ গার পেনটি খুলেচে মাগার হিজাপ খলেন নাই,1,crime
মাদারি রে এর হাতে তুলে দিয়া কুত্তা পিডান পিডা।,1,crime
দেশের লোক তোমার মত বোকাচোদা না যা বলবা তাই বুঝবে। হ্যাকারা ভিডিও ফুটেজ বানায় না তারা হ্যাক করে গোপন তথ্য নিয়ে যায়।,1,crime
মিন্নি একটা কাল সাঁপ বেসস্যা মাগী তার ফাঁসি চাই ফাঁসি চাই,1,crime
বাংলাদেশে এক নম্বর মাদারচুদ পুলিশ বাংলাদেশ থেকে পুলিশ বাহিনি তুলে দেওয়া উচিত দেশ পরিচিত করবে,1,crime
মাদারগন্জের পতিতা মাগী।,1,crime
ফাসি দে সুয়ার এর বাচ্চা দের,1,crime
তাকে ফাসি দেওয়া হোক এই কুত্তা কে। এই জন্যই দেশের এই অবস্তা।,1,crime
ভাই আমি আপনাকে একটা কথা বলতে চাই ডিসি সাহেব শুধু একবার নয় সাধনার সাথে অনেক বার সেক্স করছে মিনিটের ভিডিওটা দেখলে বুঝতে পারবেন ভিডিওটার মধ্যে উপরে তারিখ ভালো করে দেখলে বুঝতে পারবেন,1,crime
এই কুকুর বাচ্চা ফাসি চাই সরকার কে ধন্যবাদ,1,crime
তুই সালা একটা বড়ু বড়ু পাহাম কা। তার মানে তুই একটা বেআক্কল,1,crime
এর সোনার মধ্য গরম চিক দেক মাগি আর ডিসি খানকির পোলার লাওড়ার মধ্য ইট বেদে দেক,1,crime
শালার মাগী তোরা যে কুত্তার মতো অসামাজিক কাজ করবি আর বল্লে দুষ এ ই মাগী তুর ভেতরে কি আছে কি ডুকাইছে লোকে দেখেপেলছে এ ই খানকি মাগী এখনো পবিত্র হিজাবকে অপবিত্র করে হিজাব পরে আছে ভেতরের নাঁশী দেখেপেলছে হিসাবের দরকার নাই ওপেন করে রাখ শাস্তি না হওয়া পর্যন্ত।,1,crime
চোদার কথা,1,crime
অথচ কতো গুলা জানোয়ার দাড়িয়ে দেখছে আবাল বাংগালী আমরা,1,crime
গারিয়া ফুয়ার মুরামুরি দেখিয়া অও বুঝা যার যে হালায় পোন্দাপোন্দিতে জরিত আছে 😆 🇫🇴,1,crime
হলুদ সাংবাদিকতা ছাইরা দেশের জন্য কিছু করেন ডিসির বোকাচোদা কথা ই বলে দেয় সে দোষী,1,crime
একদল শুয়োরের বাচ্চা বলবে স্যারের কোন দোষ নাই। আমি তাকে বলব মেয়েটা যদি তোকে তার পায়খানা খেতে বলে তুই কি খাবি। যদি না খাস মেয়েটা হাজারবার বলক তুই যাবি কেন।,1,crime
ওই খানকির বোদা দিয়ে উট পাখির গরম ডিম ডুকানো দরকার ওর চুলকানি একটু বেশি মুরগী র ডিমে কাম হবে না। অভিনয় করে আবার।,1,crime
ছুদা লওনের পরে কী ছারের কুনো দুশ নাই বেশ্যা মাগী🐴🐴🐴🐴🐴🐴,1,crime
তুই মরি জা আমগো কি বাল নি তোর মতো বাল মরলেই কি আর বাঁচলেই কি,1,crime
থেকে মিনিট দেখেন মিন্নি কিভাবে চুপচাপ হয়ে আছে। সব দোষ এই মাগির এই মাগীরে পুলিশ ধরে না কেনো?,1,crime
বাংলার এমন জনগণই সালে রাজাকার ছিল ভাইকে সামনে মারতো কিছু করতোনা বোন মাকে ধর্ষণ করতো তাও তাকিয়ে থাকতো বেজন্মার দল এসব পাবলিক,1,crime
খানকি আবার বাঁচতে চায় সমাজে উচুঁ মাথা করে।স্যারের চোদা ভালোই লাগছে তাইলে কথায় বুঝা যায়। সুখ আর সুখ,1,crime
আসল কথা হচ্ছে টাকা গুলা সরকার খাবে এইসব ক্লাবকে জরিমানা করবে সেই টাকা গুলা ও পাবে সরকার কিন্তু এইসব ক্লাব বন্ধ করে দিবে না ঠিকি ভূল পথে থাকা মানুষ গুলা সারাজীবন ঠকে যাবে আমার বালের দেশ,1,crime
চোদাচুদি করছো তুমি আর দোষ হ্যাকার এর ।,1,crime
চুদমারানি আকাম চোদাইয়া আবার ভাব মারাও,1,crime
মাগীর পোলারা আটার জনকে না দুই হাজার জনকে দর আমাদের বোন রাফি হত্যা টা কে দামা চাপা দেওয়ার চেষ্টা করিস না প্লিজ।,1,crime
কোন স্বামীকে মারলে বা মারার উদ্দেশ্যে টেনে অন্যস্থানে নিয়ে যাওয়ার সময় কোন স্ত্রী কিভাবে এত ধীরে সু্স্থে সন্ত্রাসীদের পিছনে হাটঁতে পারে??? আমার জানা নেই। স্বামীকে কুপানোর পর স্ত্রী তার জুতা আর ব্যাগ টা আগে খুজে এটা কেমন স্ত্রী?? রিফাত কুপ খাওয়ার পর একা একাই জায়গাটি ত্যাগ করলো আর মিন্নি মাগী ব্যাগ আর জুতা খুজতে গিয়ে রফাত কে খুজেই পেল না😡 আমার মনে হচ্ছে নয়ন এখানে যতাটা অপরাধী মিন্নিও ঠিক ততটাই অপরাধী। ব্যাপার টি তদন্ত করে মিন্নি কে বিচারের আওতায় আনা হোক। মিন্নির ফাঁসি চাই ✊,1,crime
মাগি কি বলে মাগির ফাসি চাই,1,crime
এই সমস্ত বাজে কাজ যারা করে তারা তো খারাপ বুঝলাম জানিনা তাদের মধ্যে সম্পক কেমন ভালোবাসা নাকি অন্য কিছু। কিন্তু যারা এই সব ফালতু ভিডিও করলো তারা তো আরো বড় লুচ্চা খারাপ । আরে শত্রুতা মানুষের সাথে থাকতেই পারে বেশি রাগ তো জানে মাইরা ফেল এই সব ছোটলুকি কাজের কি মানে,1,crime
মাগীরে জুতা দিয়া বাইরাইয়া গাছে ঝুলাইয়া জনগণের সামনে দেখানো উচিত এ ধরনের কর্ম কাজ যেন কখনো না করে আর কেউ,1,crime
মাগী আবার পর্দাও করে! হাহাহা,1,crime
তুদের কারনে আজ বাংলাদেশ নারী দের এই অবস্তা মাগি চুদা দিবার সময় মনে ছিলনা তুর সন্তান আছে ছি ছি ছি,1,crime
লুইচ্চা সালা মাগি রে সহ তাহেরির কাছে পাঠিয়ে দেও,1,crime
কুকুরের বাচ্চা টাকে মাথা কামাইয়া চুনকালি মাইখা জুতা মাইরা জুতার মালা দিয়া সারা শহর ঘুরাইয়া পাছার উপর লাথি মইরা বেরকরে দেয়া হোক।,1,crime
মেয়েরা এরকম কেনো আর মিন্নি তো একটা খানকি মাগির সরধার মাগি বুদায় কত জোর জন কে সামাল দিতে গিয়ে এরকম হইছে এর জন্য ওই মাগি দাই,1,crime
ডিসি তো মোটামুটি বয়স হয়েছে নাকি। তো ডিসের মাইয়া আছে না আমরাও একটু আদর করতে চাই আর কি। কি বলেন সবাই। তাও যদি এই ধরনের কুলাঙ্গারদের শিক্ষা দীক্ষা হয় আরকি।। আর কিছু বলার নাই বাকিটা হেতের মায়ার লগে কইম।। আমি কি কাউকে গালি দিয়েছি,1,crime
বালের ভিডিয় মিনিট হয়ে গেল কিছুই দেখিনা,1,crime
লুইচ্ছা। হেকারেরা তোদের দুজনকে রিমট দিয়ে এক সাত করছে ঠিক বলছি না।,1,crime
মুক্তিযোদ্ধা ক্লাব মুক্তিযুদ্ধকে পন্য বানিয়ে একদল কুত্তার বাচ্চারা ব্যাবসা করে। আবার ওরাই মুখে মুক্তিযুদ্ধের নাম নিতে নিতে মুখে ফেনা তুলে ফেলে। ওদের হোগা দিয়ে মদের বোতল গুলা ঢুকাই দেয়া দরকার ছিলো। হালারা মাদার দ। আমি কি এখানে কাউকে গালি দিয়েছি? তারপরেও একদল লোক কমেন্টের রিপ্লাইতে আমাকে দুয়ো দিবে।,1,crime
শালার কথা বার্তা শুনে ই বুঝা যায় সে কাজ টি করেছে,1,crime
ওর চোখ দেখেই তো বোঝা যায় লুচ্চা 🤭🤭🤭🤭,1,crime
তদন্ত করার দরকার কি ভাই এই দেশে কি ধর্ষনের শাস্তি হয় ওরা ত দুজনেই ইচ্ছে করেই এসব করেছে। দোশ দুজনের । শাস্তি দোজনকেই দেন। ধর্ষনের এর জন্য নয় বরং এমন বিকৃত যৌন অপকর্মের জন্য এদের দোজ়নকেই শায়েস্তা করা উচিত। ধর্ষন নাম দিয়ে বেইশ্যা মেয়েটাকে বাচিয়ে দিয়া উচিত হবেনা।,1,crime
এই গান শুনায় কাপড় খুলতেন ডিসি সাপ।,1,crime
সালাতো খুবই দূর্বল। ঢোকানোর আগেই আউট 😡😡😡😡,1,crime
চোর চুরি করে কি শিকার করে সালারে চাকরি থেকে বরখাস্ত করা হোক আর কঠিন শাস্তি দিক এটা আমার দানি,1,crime
আসে পাসের মানুস গুলা সব হিজরা জন রে জদি সবাই মিলে দরতো তো ছেলেটা আজ বেচে জেতো হায়রে বাঙ্গালি,1,crime
নারীবাদী শুয়ারের বাচ্চারা কই খানকির পোলারা এখন কই গেলি তোগো মাইরে চুদি আমি। তোগো জন্য মুখ ভালো রাখতে পারিনা। মোচয়ালা টাকলা সালাদের টিভি পর্দায় চাপাবাজী কই গেল,1,crime
মাগির লজ্জা নাই আবার মুখ ঘুরছে নটির বাচ্চা একতো চুদা লইছিস বড়বড় কথ্,1,crime
তুই সালা একটা মাদারের বাচ্চা।,1,crime
আবার তদনতো এই বাল সুনলেই মাথা গরম হয়ে যায়,1,crime
মূল পরিকল্পনাকারি তো এই শয়তান মিন্নি সন্ত্রাসী নয়নের সাথে তার বিয়েও হয়েছে পূর্বে। পরিবারের চাপে পড়ে রিফাত কে বিয়ে করে তাই সে নয়নের কাছে যাওয়ার জন্য রিফাতকে হত্যার নকশা আঁকে সে।। আর সাংবাদিক কুত্তাকে বলি এইসব ভুয়া নিউজ বানানো বন্ধ কর আসল ঘটনা আমরা ভালো করেই জানি।,1,crime
প্রকৃত ঘটনা আর কি জানার আছে জাতি সবই দেখছে। শালা মিডিয়ার বাচ্চা দালালি করলে কিন্ত খবর আছে,1,crime
আ কি কুড়া কইরা কান্দে গো লুইচ্চার দুরতম ফাসি দেখতে চায় জনগণ।,1,crime
এই সমস্ত কুলাঙ্গারদের কারণেই আজকে মেয়ে জাতি এত অবহেলিত বঞ্চিত বঞ্চিত ধর্ষিত,1,crime
এই শালির মেয়া তর বাবার সাথে চোদা চুদি করিয়া।এখন কস আমি কিছুই জানি না নাটক তো ভালই জানোস তর এই মুখ মানুষের মাঝে কিবাই দেখাবি তুই মরে জা নটি।আর জদি না মরস তাহলে টাংগাঈল নটি পাড়ায় ভরতিহ মাগি,1,crime
এই জানোয়ার দেশের মানুষ কি অাবাল। তুই বলবি তোকে হ্যাকার হ্যাক করছে। অারে পাপে বাপরে ও চারেনা।,1,crime
ঠিক কথা বলছেন। ঐ সব ব্যাস্যা চেতনাবাজ দালালরা এখন কথা বলেনা। আমার জানা মতে কোন ভাল মানুষ কুত্তালীগ করতে পারেনা। লীগ মানেই আকাম কুকাম।,1,crime
বালের মিডিয়াগুলা পারেও মাতামাতি করতে।,1,crime
বোকা চোদায় কয় কি,1,crime
রাস্তার ম সাড়ে দশটা থেকে সাড়ে ঠেলা খাইতে ভালো লাগছেনা শালিমা আগে পুলিশ প্রশাসনের এখন উচিত দরকার ছিল সোনার মধ্যে মরিচ দি যোগাযোগ,1,crime
এদের দুই জন কে কেউ তো দড়ি কলসি দাও কোন পঁচা নর্দমা তে ডুবে মরুক 💚💚💚💚💚💚💚💚💚💚💚💚💚💚💚💚💚💚💚💚💚💚💚💚💚💚💚💚💚💚💚💚💚💚💚💚💚💚💚💚💚💚💚💚💚💚💚💚💚💚💚💚💚💚💚💚💚💚💚💚💚💚💚💚💚💚💚💚💚💚💚💚💚💚💚💚💚💚💚💚💚,1,crime
এদে হেডাদীয়া ডিম গরম করে দেন,1,crime
শালার পুতরে ফাঁসি চাই,1,crime
মিন্নি বেস্যা,1,crime
বোকা চোদা তোদের কি কাজ কান নাই কাংকির পোলা রা ফাইজলামি করোস,1,crime
বুক চুডা,1,crime
কুলাঙ্গারের বাচ্চা করেছে কি,1,crime
ছি মাগি ছি কেমনে মিথ্যা কথা বলে দেকছোনি,1,crime
জুতা মারার দরকার মাগীরে,1,crime
লুচ্চা ডিসি র কোন দোষ নাই এটা বিএনপি র চক্রান্ত,1,crime
হা😛হা😜হা😝 সরকারী লোকজনের দ্বারা এইসকল অপকর্ম হওয়া স্বাভাবিক। কারন তাদেরকে বিচারের কাঠগড়ায় দাঁড়াতে হয়না। এরা দলীয় প্রভাবে নিয়োগ পেয়ে থাকে এবং তাদের কোন শাস্তি হয়না বাংলাদেশে। সব সরকারের অামলেই তারা পালিত কুত্তা হয়ে থাকে,1,crime
তুমার খালি চোদার ইচ্ছা,1,crime
মাদার চুদের বাচ্চাদের সরকারি চাকরি সুদায় তাই আরকি,1,crime
সালা পারেনা বল নাই,1,crime
আমার মনে হয় মিন্নি ভাবছিল এই ছেলেরা ওর জামাইকে কিছু উত্তম মধ্যম দিয়ে ছেড়ে দিবে কিন্তু এটা হয়তোবা ভাবেনি যে এই কুত্তাগুলা রিফাতরে খুনের মতলব আটছে,1,crime
কুওারা এসব করেও রেহাই পায়,1,crime
তোরে চুদব কত টাকা চাস,1,crime
আওয়ামী হারামজাদা কথায় বড়।,1,crime
মাগি মিনিকে চোদুম,1,crime
আওয়ামী লীগের কুকুর দালাল জারজ,1,crime
এই বাইঞ্চদের কটিন বিছার হওয়া দরকার কি ছলছে এইশব,1,crime
খানকির পোলা অন্ন মেয়েকে কে কেনো তোর মেয়েকে নিয়ে গিয়ে চুদতি,1,crime
ঘড়ে এত সুন্দর বউ রেখে কেন যে ধরা খেলে এ জীবনে মুখ কি ভাবে দেখাবে জানিনা জানি শুধু জামালপুরের ডিসি ছিল লুইচ্ছা বদমাইশ হারমজাদা জন্মগত নারি লোভী।,1,crime
একটু ঢেলে দি তো বিতরে ঢেলে দে নাই তোকে তো দিয়ে হবে না তোর জন্য দরকার ভারতের মদি কে এক রাত কত টাকা তোর মাগি কথাই কার 😡😡😡😡,1,crime
এই এখানে কোন হৈচৈ আছে না কালকে দেখবেন এক বলবে ডিসি সাহেব বালা না আমি তো বলি আমি তো বালানা বালা লইয়া থাইকো ডিসির এমন মেয়ে থাকতে আরেক জায়গায় যায় বদমাইশ,1,crime
হালার পুত পাগল বালের ভিডিও বানাছ,1,crime
মাগি স্যারের চোদা খাইয়া পাগল হয়ে গেছে,1,crime
তোর ছাগল মেয়ের কি দুষ তুই কই ছিলিরে,1,crime
জনগণ এর সামনে নিয়ে জুতার বারি দিয়ে বেজ্জত করুন এই জানোয়ার কে,1,crime
এই কুত্তার বাচ্চারা দেশকে অশান্তি করে তুলছে। এই বেয়াদবকে থানায় ঢুকিয়ে একটু খাতির যত্ন করলে বের হয়ে যাবে।,1,crime
কুজনিয়ে দেখেন ছাত্র জীবনে কুত্তালিগ করচে ।অব্বাস জায়নাই,1,crime
চুদা নিবার সময় মনে থাকে না ডং,1,crime
মিন্নি শালি বেশি দোষি,1,crime
তর মত মাগী জননো আজ আমরা সবাই কলঙিত,1,crime
হ্যেকার গ্রুপ কি ওর মায়্রপ চুদতে চাইসিলো,1,crime
খানকীর পোলা সব পা চাইতে বি সি এস পাস কইরা হয় আমলা। দেশের প্রজা হইয়া ভাবে দেশের রাজা হইসে আর যা মন চায় তাই করে। কুত্তার বাচ্চাদের নুনুটা কর্তন করা উচিত।,1,crime
হালার পুতেরে পুটকী দিয়া গরম ডিম ডুকায় দেয়া হক যাতে তার মৃতু হয়,1,crime
নুনু চুশছেন যে তখন তো ভালো লাগছে,1,crime
এরা জানোয়ার বাচ্চা এদের জরমের ঠিক ক নাই,1,crime
আমার মনে হয় তুই মাগির দালাল,1,crime
এবার মিন্নি বলবে এগুলো এডিট করা যায়। কুত্তীর বাচ্চা।,1,crime
সালা আবাল ডিসিকে আবার সাহেব বলছে!!তোকে আর গালি দিয়ে গালিকে লজ্জা দিতে চাইনা।ফালতু কথা বলে সময় নস্ট করলি।,1,crime
দুই জনে ঘন্টা সেক্স করছে এর পরে ও দোষ নাই এই মাগির পেটে ডিসির বাচছা আছে,1,crime
আমার বালের ভিডিও হইছে মিন্নী মাগীর দোষ তুলোস নাই কেন ভিডিওতে। ঐ মাগীইতো বড়ো খানকি।,1,crime
খানকির বাচ্চা,1,crime
নিজেই লুচ্চামি করে নিজেই তদন্ত বাহ বাহ। এই হল অবস্থা,1,crime
মাগির সোনা দিয়ো গরম ডিম ডুকিয়ে দিলে সব কিছু বলে দিবে।,1,crime
এই দেশে কী বিচার নাই এতো মানুষ কে কুপিয়ে মারলো একজনার ও বিচার দেকলাম না কত মায়ের কোল খালি করবে এই জানোয়ার রা।,1,crime
মাদারচুদ এদের কি শাস্তি হওয়া উচিৎ,1,crime
মাগির ঢং কতো,1,crime
শালা লুইচ্চার অঙগি বঙগি দেখলেই বুঝায় নাম্বার ওয়ান লুইচ্চা সাবাই এর বিছার ছাই,1,crime
মাগি তুই মরসনা কেন,1,crime
মিন্নির পাছার ভিতোরে গরম ডিম ডুকিয়ে দিলে সব কিছু বলে দিবে,1,crime
কিছু কাজের না সব শালারা ভাবেন না নাটক তো ভালো করতে পারো,1,crime
সালা লুচ্চা ভাই ওরে পিটাও,1,crime
এই মাগির জন্য না জানি আরো কতো ভাইদের মৃতু হবে মিননির ফাশি চাই,1,crime
হাইরে মানুষ মিন্নির দোষ দিয়ে হত্যাকারীদেরকে আমরা আরাল করে ফেলতেছি। আর কিচু আবাল আছে শুধু হ হ করে।,1,crime
শালা খানকি মাগী তোর পুটকিতে গরম ডিম ঢুকাতে হবে। পুরো ভিডিও তে পরিষ্কার বোঝা যাচ্ছে। তারপর ও স্বীকার করছে না। ধরা খাইলে চোরে কি বলে আমি চুরি করেছি।তোর সন্তানের কথা চুদার আগে মনে ছিলো না।,1,crime
এই কেমন পাবলিক। একটা পাবলিক ও দরলো না।সব মাদারছোদ,1,crime
সালার বিচি কেটে দেওয়া দরকার,1,crime
ওই হালার সুনাই খান ইট ঝুলায় দেয়া উচিৎ,1,crime
শালী মজা খাওয়ার সময় মনে থাকেনা,1,crime
খানকি টাকা কতো পাইছো,1,crime
ওই পাইস সেরভাইসেস আবালের যদি বাংলাদেশের শেষ সীমানায় পাতাম তোর কুপে আমি হত্যা করতাম বিশ্বের সকল মুসলমানের মুসলমানের খুন করা ওর গুষ্টি পাঠিয়ে দিতাম,1,crime
এই শালা মাগীর ব্যবসায়ি! মেয়েকে দিয়ে দেহ ব্যবসা করিয়ে অনেক টাকা কামিয়েছে। সে নিজেও সুদের ব্যবসা করে। এখন ধরা খেয়ে মাথা নষ্ট! কুছুই বুঝে না সে ছোট মানুষ বাচ্চা ফালায়াছে!,1,crime
কি তদন্ত করবে কে আসল ভিডিওটা করল তাকে খুজে বের করবে নাকি হারামজাদাকে জুতা পেটা করা উচিত,1,crime
এই মেয়ে বৌ নামের ডাইনি,1,crime
সালা খানকির পুলা,1,crime
অফ আল্লাহ এসব আর কতো দেখবো এসব কুওাদের বিচার কি হবে এসব দের জন্য ভালো ভালো অনেক ছেলে মরে যাচ্ছে 💆😡ভালো ছেলেদের কপালে কেন যে এসব কুওি চেরি গুলি এসে পড়ে 🙄💆😫😡😞,1,crime
জ্যনতো আগুনে পুড়ানো উচিত কুত্তা গূলোর,1,crime
এক কথায় অসাধারন সেক্স ডিসি সাহেব আপনাদের মত লোকদের আরো এমন অসাধারর সেক্স আর চাই তার কারন আপনারা এ দেশের কুলাঙার সনতান,1,crime
তোমার চ্যানেল চুতিয়া পুরা ভিডিও দেওয়া হয় না,1,crime
স্যারে দোষ নাই তাহলে কি তোর দোষ মাগি,1,crime
মাগিখুনি। বিচার চাই,1,crime
কুনো মোহিলা বিপদে পোরিয়া থানায় গেলে পরে বুযেযে আমার থানায় নাযাওয়াই ভালো আছিলো আগেনা হয়তো আমার টাকাগেছে কখন ইজ্জত সহগেলো কুনো মোহিলা পাইলে জতখন চুদবার নাপায় ততখন পরেন্ত মোহিলাকে সান্তি দিবোনা যোদি চুদবার নাদেয় তাইলে খুব ডরবয় দেখায় তাইলে চুতে দিতে বাদ্দ,1,crime
সব সালার হারাম খোর জে বর কোন পদে বসে খানকির পোলারা ঘোষ খাইয়া টাকার পাহাড় গড়ে আমাদের দেশের আইন শৃঙ্খলা পরিস্থিতি দুর্বল তাই জে কেউ এই রকম সাহস পায়,1,crime
এই মাগি,1,crime
মাহিকে দরে চিদকরে বতার ভিতরে সরিচের হুডাওলবন ডুকাইয়া দেও,1,crime
অা হা রে তুই সমস্ত মা জাতীর কলঙ্ক তবুও জানোয়ার টার পক্ষ নিলি,1,crime
এইখানে থাকা এক এক টা পাবলিক এক একটা হিজরা। 😡😡,1,crime
মিন্নির নামটা শুনলে রক্ত মাথায় উটে যাই আমার।তাকে কেন বাঁচিয়ে রেখেছে?? মিন্নি আর মিতু দুই মাগীরই ফাঁসি চায়।।,1,crime
সব করছে ওর বউ 👉👉👉 মিন্নীমাগি এর জন্য বেসি সুন্দরি বউ ভালো না মনে করেন কাল।সাপ ওর বউকে দেখলে।ই বুজা যায় কিছু লুকাচ্ছে,1,crime
বদমাইশি করবে তুমি আর তদন্ত করবে সাংবাদিক মাগি ব্যইমান ধুকাবাজ নিজ স্বামীর সাথে প্রতারক কারি কলঙ্কিত তুই তোমার তদন্ত করে তোমাকে শাস্তি দেয়া হবে তোমার কারণে আজ ডিসির জীবন ও তার পরিবারের জীবন শেষ হয়ে গেলো।,1,crime
ডিসি শুয়োরের বাচ্চা আর ওই জাওড়া মাগির ফাসি চাই।,1,crime
এই ধরনের বড় অফিসার যারা আছে সব হারামি পাওয়ার পেয়ে এই সব করে এই কুওার বাচ্চা মিথ্যা বলছে এদের জেল দেওয়া উচিত যারা রক্ষা করবে তারা বক্ষক,1,crime
দুর্নীতি বাটবার ঘুশ খোর মাগিবাজ কথায় কথায় পুলিশের ভয় দেখায় অসভ্য জারা বর পদে বসে আকাম কুকাম করে এদের বিচার হয় না,1,crime
সালা তোরা তো মানুষ না জানুয়ার ঘটনা ঘটাস প্রতিবাদ করতে পারিসনা সালা বাইনচুদরা,1,crime
যেই ভিডিয়ো করুক।এটা সত্য।দেখেন ঐ শালারপুত কিভাবে কেমারার সামনেই মছোর পারছে।এই মছোর পারার মানে ও আনেক টেনশনে আছে।এখন কি করে বাজতে পারি।,1,crime
সে এক পতিতা সন্তানের কথা যদি চিন্তা করতো তা হলে সে এই এমন কাজ করতে পারতো না।।।,1,crime
শালি ডাইনি মাগী ওকে আইনের আওতায় আনতে হবে ও পথম আসামি তার পরে ওর মাকে ও গরম ডিম দেবার দরকার,1,crime
মাগির পোলারা এখন মায়া কান্না করে লাভ নাই জেদিন জীবন্ত লাশ নুসরাত আগুনে দগ্ধ অবস্থায় চিৎকার করছিলো সেদিন তোদের চোখের পানি কি শুকিয়ে গেছিলো এখন সময় এসে তোদের যতো পারিস কান,1,crime
বেচারা পাইসা গেছে বেয়ানছোত কা বাচ্চা,1,crime
অারে মাদারচুদ বরগুনার কলেজের ছাএরা এবং কাপুরুষের দল চেয়ে চেয়ে দেখছিল কোপানো।অার পুলিশকে বলছি মিন্নী হল এক নাম্বার আসামী। সে সরাসরি জরিত,1,crime
সালি একটা মাগি,1,crime
জানোয়ারটাকে রাসতার উপর ফাসি দেওয়াহোক যেন তাকে দেখে আর কোন জানোয়ার যেন এমন কাজ করতে না পারে,1,crime
এই মাগীর কোন ক্ষমা নাই।আর ঐ শালার পোলার লিঙ্গের মধ্যে এক টন ওজনের পাথার বেধেঁ দেওয়া হোক।,1,crime
এটা শুদু বাংলাদেই সম্বভ অপরাধ করে আবার নিজেই তন্দথ কারি এ গুলা হাসিনার পালিথ কুকুর,1,crime
মালে দরা কাইছে একন কান্না করে কেন মাগি,1,crime
তুই জানোয়ার,1,crime
আবাল চুদারা রোহিঙ্গা,1,crime
লুইচ্চা জেলা প্রশাসক সারাদেশের পাবলিক এখন তোর সেক্সি ভিড্যু দেখবে। ছিঃ ছিঃ তুই বালতি বিষ খেয়ে মরি জা 😂😂,1,crime
ওই মাদার ছুদেরা এখন কাদছ কেন ওদের ফাসি চাই,1,crime
মিনি শালিকে ফাঁসি দেওয়া হোক,1,crime
খানকির পোলারে দেখতেই লুচ্চা দেখা যায়,1,crime
সালান এতো লোক তোরা কি করলি,1,crime
এই কুত্তার বাচ্চা বেজন্মা উপস্হাপক নিরীহ একটা মেয়ে কে আগুনে পুড়িয়ে মারার সময় তুই কোথায় ছিলি রে খানকির পোলা?,1,crime
মিন্নি মাগী ও সাথে জড়িত কি একমত?,1,crime
এই লুইচ্চা ডিসি তোর মরে যাওয়া উচিৎ তুই মিডিয়ার সামনে মুখ দেখাছ কি করে ছি ছি ছি,1,crime
রুমে ছিল দুই জন ছেরির ছিল মন ডিসির ছিল দন এক করছে দুই জনদেখেছে জনগন,1,crime
কানকির মাগি বড়ো ক্রিমিনাল,1,crime
খানকি মাগিটাই এই জঘন্য হত্যার মূল হোতা এতে কোন সন্দেহ নেই।,1,crime
ওই কুত্তার বাচ্চা মিন্নি😠😠 তোর সাপোর্ট নিয়া কথা বলসিমান প্রথমে ভাবসি তোর কোনো দোষই নাই😠😠 কুত্তার বাচ্চা তোর কারণে আজ রিফাতের এই অবস্থা হইলো তোর ফাসি চাই সবার আগে😠😠,1,crime
সালাদের বিচিতে আদলা ইট বেঁধে দেয়া হোক,1,crime
কুলাংগার সন্তান জন্মদিলে এইসব কান্নার মুল্যে নেই প্রথ্যক মা বাবার কষ্ট লাগবেই এটা সাবাবিক,1,crime
আশলে ভাই একটা ছেলেকে এতো গুলো লোক মারলে এবং কুত্তার বাচচারা চেয়ে চেয়ে দেখলো সবাই জদি আশে পাশে মানুষ তদের কে ধরতো ওরা এই কাজ টা করতে পারতো না আর জদি মিন্নি মাগি কুপানোর আগে চিল্লা পাললা করতো তাহলে ওরা মারতে পারতো না ওই মাগি সব করায়ছে ওই মাগির ফাসি চাই কারন এতো মানুষ এসে তোর কলেজের থেকে তোর সামিকে ধরে নিয়ে জাইতেছে আর ও কি না টালু মালু চেয়ে চেয়ে হাটছে আমি শুধু ওর বিচার চাই সামি মারা বিচার সবাই কি বলেন,1,crime
মূল দোষী মিন্নি বালের নিউজ,1,crime
দেখতে মাগীর মত,1,crime
মানুষের রুচিবোধ এতটাই নিম্ন পযায় চলে আসছে কিছু মানুষ ত এখন জানোয়ার হয় যাচ্ছে। ছিঃ,1,crime
ওই মাগী ফাসি চাই,1,crime
এখানে জনগন সব চোখ থাকতেও অন্ধ সালারা তুদের মত পাবলিক এর জন্য আজকে এই অবস্থা। তুরা হিজরা।।।,1,crime
স্যার আমার কোন খতি করে নাই আগেই আউট হয়ে গেছে সালার মাগি,1,crime
ওই মাদারচোদ ডিসিকে বাজারের মধ্যে নেংটা করে পিটানো দরকার এবং ওই নারীর এখানে কোনো দোষ দেওয়া যাবেনা কারণ ওই নারী ডিসির অধিনে একজন কর্মচারী তাই ওই নারী ডিসির বিরুদ্ধে অভিযোগ করেও টিকতে পারবেনা আমাদের সমাজে একজন নারী নিরাপত্তা কতো টুকু হয়তো ওই নারী ডিসির বিরুদ্ধে অভিযোগ করলে হয়রানির শিকার হতো তাই হয়তো ওই নারী ডিসির বিরুদ্ধে অভিযোগ করার সাহস করেননি ওই নারীকে নিয়ে টানাটানি না করে ওই মাদারচোদ ডিসিকে বাজারের মধ্যে নেংটা করে পিটানো উচিত একজন নারীকে যদি প্রতিদিন একটা ধর্ষক কুত্তা যৌন হয়রানি করেন তাহলে একজন নারীর পক্ষে কতক্ষণ টিকে থাকা সম্ভব তাও আবার ধর্ষক ডিসি তার অধিনে চাকরি করে ওই নারী ওই নারীতো ডিসিকে যৌন হয়রানি করিনি প্রতিদিন যদি ওই কুত্তার বাচ্চা ডিসি ওই নারীকে উত্ত্যক্ত করতে থাকে ওই নারীর পক্ষে কি বা করার আছে ওই নারী অভিযোগ করবে কার কাছে ওই নারী যদি মাদারচোদ ডিসির বিরুদ্ধে অভিযোগ করতো তাহলে হয়তো ওই নারীর পক্ষে টিকে থাকা সম্ভব হতোনা তাই হয়তো ওই নারী ডিসির বিরুদ্ধে অভিযোগ করেননি তাই একজন নারীর দোষ খোজার আগে পর্দার আড়ালে ওই নারীকে কিভাবে ভয়ভীতি প্রদর্শন করে যৌন লালসার শিকার বানিয়েছেন সেগুলো আগে খুজে বের করা দরকার বাংলাদেশে ওই মাদারচোদ ডিসির মতো আরো অনেকে আছেন যারা প্রতিনিয়ত এমন হাজার হাজার নারীর সর্বনাশ করিতেছে যাহা আমরা জানি না তাই এই ডিসির বিরুদ্ধে কঠোর শাস্তি ব্যবস্হা করা হোক,1,crime
আসলে আপনার রা মানুষ নামে জানুয়ার,1,crime
সুয়োরের বাচ্চাকে জুতা পিটা করা উচিত ছিল,1,crime
নয়ন কুত্তার বাচ্চারে প্রকাশ্যে জবাই করা হোক,1,crime
লুচ্চা ডিসিকে বরখাস্ত করা হউক,1,crime
ভাইয়া এই কুকুরের বাচ্চাদেরকে ধরে জবাই করো সরকারের হাতে চলে যাও যত তাদের ফাঁসি দেয় তাদের ফাঁসি দেওয়া উচিত ছেলেদের জায়গায় মেয়েরা কেন ও যদি এতই ভালো হতো তাহলে ওখানে কি করে দুই গালে দুইটা থাপ্পড় দিয়ে মাথাটা উঁচু করে দেন তারপর ঠিক হয়ে যাবে,1,crime
যানোয়ারের বাচছারা তোরা। আমার থাকলে তোদের এমন দসা করতাম তোরা দূনিয়াতে থাকবি যতদিন দুনীয়াতে থাকবি ততদিন মনে রাখতে হভে।,1,religion
অন্যের সমেলচনা করে ইউটিউবের টাকা তর মা বাবাকে খাওয়াজ ?? আসপোস তর মত কুলাঙ্গার এর জন্ম দিয়েছে তর মা বাবা ????? তাহসিন,1,religion
কিরে তাহেরি তুই বলে পীর তুই বড় শয়তান তুই মুনাফিক নাস্তিক এজিদতের ব শধর,1,religion
বেয়াদবের বাচ্চা । বাল ডি তো ঠিক মতো উঠছে না ।,1,religion
এই সব জারজের বুকে ডাইরেক্ট গুলি তবেই ইসলামে শান্তি ফিরে আসবে,1,religion
👏👏👏 ভাই তালি টা ছিলো ওই শালার পাছা মোবারকে👋👋👋👋,1,religion
ভন্ড দেওয়ানবাগী একটা কুত্তার বাচ্চা ???,1,religion
নাস্তিক বাচ্চা নাস্তিক রা কেমন করছে কুত্তার মতো ঘেউ ঘেউ করছে,1,religion
সালারা গাজা খোর,1,religion
ঐই মাগী তুই দেখসিস আল্লাহ কি রকম। যে যেরকম সে সেরকম শাস্তি পাই। তুইও পাবি দেখিস।,1,religion
এ শালা বাল পাখনা বুঝে না কিছু খালি ছিল্লায়!,1,religion
এই শালা মাজার পুজারিরে জুতা মারেন তালে তাল,1,religion
কুত্তার বাচ্চা তাবলীগ বিরোধী কথা বলরে তোরে জুতা পেটা করবো খানকির পোলা তোর ভন্ড চুদি তোর জন্ম ঠিক নেই জারজ তুই,1,religion
তোর কপাল পুড়ছে জানুয়ারের বাচ্ছা।,1,religion
শালার পোলা কি নামে গুজব খাওয়া ঠিক কোন হাদিসে আছে মানুষের মানুষ গান,1,religion
চুদেন সালিকে,1,religion
ওই কুলংগার তুই ফেসবুক চালাও কে এটা তো সানিলিয়ন চালায় এরা জমানার শেষঠ দাজজাল তোরা যখন নেট চালাও তখন কি কি ইসকিনে চলে আসে তা আমরা জানি শয়তানের উত্তরশরী,1,religion
মাইন্দারপো কয়কি,1,religion
জুতা দিয়া দিমু হালারপো কুতারবাচচা,1,religion
এই শোওরের বাচ্চা,1,religion
এই সব পাগল ছাগলের দল যে কই থাকে,1,religion
তোর মা বোন কে চুদি মিথ্যা তথ্যা দিস,1,religion
সালাই ভন্ড,1,religion
মুরগি চোরা শাহরিয়ার কবির। পতিতা খানকি।,1,religion
মাদারচোদ তোফাজ্জল হোসেন ফালতু কথা বলে,1,religion
আমি ভারত থেকে বলছি এই ভন্ড শালা কে জুতা মেরে মাহফিল থেকে বের করে দাও,1,religion
এই মাগির বাচ্চা তদের একদিন বিচার হবে মনে রাখিস তদের মরতে হবে আর ভাই আপনি তো এই ভিডিও ভাইরাল করতাছেন কেন আপনি তো আপরাত করছেন,1,religion
কত্তার বাচ্চা,1,religion
আরে ভাই তুই তো একটা। জারজ সন্তান এর জন্য মিজানুরের সম্পরক বাজে কথা বলেন,1,religion
কুত্তা বাগি গালে জুতা মারি,1,religion
জানোয়ার শালা কুত্তা তোর গালে জুতার বাড়ি,1,religion
ভাই শালাদের জুতা মার,1,religion
এই সব নাস্তিক পুরুষ মহিলা বাংলাদেশে আর যারা যারা আছে সব গুলারে জুতা পেটা করে অং সাং সুচীর দেশে পাঠিয়ে দেয়া উচিত হউক।,1,religion
হালার পোয়া তোরে কয়জনে চুদে,1,religion
খানকি মাগির পুলারা তুদের বিচার একদিন হবে,1,religion
মাদারচুদ তর আলেম থাকলেই কতটুকু আছে বল মাদারচুদ তকে ব্যবসাই লামাইছে বাইনচুদ গান্জট্টি তরে চিনে কোন হালাই রে মূর্খচুদা তাহেরির জুতা টানার জন্য ও তকে নিবেনা বাইনচুদ,1,religion
সবগুলাকে ধরে কুত্তার গু খাইয়া দেয়ার দরকার😈😈😈👹💀👹,1,religion
অ সালার পুত তর জন্ম কোন সালে রে,1,religion
বাল উঠেনি বেটা বড় বড় কথা বলিস। মূর্খের কীটপতঙ্গ তুই। লুঙ্গী খুললে তো মনে হয় দেখা যাবে নুনুর মাথা কাটা নাই ব্যাটা তুই আসছিস ওয়াজ করতে।,1,religion
তুইবালপাকনা,1,religion
সালা বনডা হেরে পাইলে মার মোও,1,religion
আমার তো তোমাকে গালার খুব ইচ্ছে করছে কারন তুমি একজন মুসলিম হয়ে তোমার মাথায় টুপি নাই আর ভিডিও বানাচ্ছো সারা দেশের মাঝে মুসলমানদেরকে নিশা দেখাচ্ছ হিন্দু মুসলিম সবাই তো ভিডিওটি দেখছে ত মুসলমানির তো বদনাম হচ্ছে শালা কুত্তা,1,religion
তাহেরি ভন্ড ওই কুত্তার বাচ্ছারে পাইলে ওর মুখে জুতা মারবো হালার ভন্ড বেয়াদব।,1,religion
বাস্টার্ড মুরগী কবির,1,religion
শালায় একটা মাদারচোদ,1,religion
ওই খানকির পুলা কোরানের কি বুজোস তুই ওই আল্লাহর আকার নাই আছে তা তুই কোরান পরছেসো নটির পুলা হুম কোরানে লেখা আছে জখন দুনিয়া সেশ হবে জাহান্নামের আগুনের খুদা মিটবে না দোজগ বেলে আরো দেও তখন আল্লা নিজের পা মোবারক দুজগে দিবে দুজগ বলবে আর লাগবে না ওই সালার পোঃ এখানে আল্লাহর পা কই থেকে এলো বল সালা রাসুল পাক আল্লাহর বন্দ্বু তাহলে আল্লাহর সব দেখতে রাসুল পাকের মতো শালা তুই বদমাইস তোর উপরে গজব পরবো মনে রাখিস কার বিতর কি তা তুই বুজবি কি আমি দেয়ান বাগির মুরীদ না তবে তোর কথার সুনলে তোরে জুতা দিয়া পিটাইয়া সামান দিয়া গোসল করামু তুই কি বুজোস শালা বদমাইস কারো গিবাত করা আর মরা মার গোস্তো খায়া এক সমান সালা তুই টাকা কামানোর জন্য এমন,1,religion
এই বেয়াদফটা নাম্বার ওয়ান বন্ড,1,religion
তুইও গাধা তোর ওয়াজ যারা শুনতাছে তারাও গাধা শালা আবাল মার্কা ভন্ড,1,religion
ভাই তুই জিবনে এতো দিনে একটা ভালো কাজ করছোছ। খানকির পোলারে হোগ 😂😂😂😂,1,religion
এই নাস্তিক কুত্তার বাচ্চাদের আল্লাহ এমন শাস্তি দেওয়া হোক আর এই দুনিয়ায় এ কাজগুলো জনকে করতে সাহস না করে সবাই বলুন আমিন,1,religion
জারছ ভন্দ,1,religion
শালায় মাল খায়া টাল হয়া গেছে,1,religion
কুকুরের বাচ্চাদের দের কে জুতা করে পিটান আর আপনারা যদি না পারেন তাহলে ভারতে পাঠিয়ে দিন কলকাতায় তার পরে দেখে নিবো,1,religion
জন খানকির মাগি আর খানকির পোলারা বেশি গেন দেখাইতাছে হুজুর এর উপর বাল পাক্নামি করলে জইলা যাবি,1,religion
দেওয়ানমাগী। 😂 দেওয়ানমাগী। 😂 দেওয়ানমাগী। 😂,1,religion
বাঘের বাচ্চা একজন। শিয়ালের বাচ্চা চারটি।,1,religion
জামায়াত শিবিরের কুকুররা সারা ইউটিউব দখল করে নিয়েছে।,1,religion
দেওয়ানবাগী কে আমার কাছে পাঠিয়ে দাও ওকে আমি আমার হাগু খাওয়াবো।যাতে করে সালা আর মিথ্যা কথা বলতে না পারে।,1,religion
কুততার বাচ্চা,1,religion
খানকি মাগি তুইতো একটা বেশ্যা,1,religion
নোমানি তুই বনড জারজ কুলাংগার বদমাস লুচচা তরে পাইলে জুতাদিয়া বাইরাইতাশ সইতানের বাচাচা বদমাস ফেতনাভাজ,1,religion
ভন্ড দেওয়ানবাগীর মুখে কে কে মুতি দিতে চান আপনারা লাইক দেন।,1,religion
ওই হালাই দারাইছে ওরে আমি পাইলে জুতা দিয়ে পিটাইতাম,1,religion
খোদার কসোম এদেরকে পেল এতোটুকরো টুকরো করবো কুত্তা খেতে কনো ওসুবিধা হোবেনা,1,religion
হায়রে ভন্ড মাদারচোদ,1,religion
বাই দেওয়ান বাগি কুত্তার বাচ্চার ফাসি চাই,1,religion
ওর মা র ভোদায় থেকেই বাল পাখনা হয়ে বের হয়েছে। বছর বয়সী শিশু বক্তা ।,1,religion
দেওয়ান বাগি কুকুরের চেয়েও খারাপ,1,religion
সরকার কই সেটা আমি বুঝতেছিনা। সরকার কি দেখেনা এইসব। আর জনগণ কই। তারা সিফাতুল্লাহ কে নিয়া নাচা নাচি করতে পারে কিন্ত নিজ দেশ এ এই জারজ টাকে কি কেউ কিছু বলতে পারেনা৷ অস্তাগফিরুল্লাহ নাউজুবিল্লাহ এইসব কথার কাছে হার মানে। লজ্জা এইসব একটা মুসলিম দেশ এর জন্য,1,religion
তোরে ধারে পাইলে জুতায় গু লাগাইয়া পিডাইতাম হালা ভন্ড,1,religion
শালারে জুতা পিটা করা উচিত,1,religion
ভিডিও অাপ এর সাথে ওলটা পালটা ক্যাপশন গুলো জানোয়ার এর বাচ্চারই দিতে পারে।,1,religion
যেই মাগির বাচ্চাগুলো ডিজলাইক দিছে তারা দেওয়ান বাগি নামক খানকির পোলার মুরিদ।,1,religion
তার মুস দেখ মাদার চুদ,1,religion
নাস্তিকদেরকে জবাই করতে হবে।,1,religion
সালা তাহেরি তোর বাবার নাম আবুজেহেল,1,religion
মিজানুর রহমান আজহারী তুই তো ব্যাটা ওহাবীদের দালাল তোর মুখে এসব কথা মানায় না শালা মূর্খ,1,religion
এই ভন্ডদের মুখোশ খুলে ফেলার জন্য আর সাধারণ জনগণকে সচেতন করার জন্য ধন্যবাদ আপনার নাম জানিনা কিন্তু আপনাকে আরো অনেকককক বড় ধন্যবাদ দিতাম যদি আপনি এই মাগীর ছাওয়ালদের আরো উত্কৃষ্ট মানের নিম্নতম ভাষায় আরো বেশী গালাগাল করতে পারতেন ব্রোঃ আপনার পক্ষ হয়ে আপনার মা বাবার কাছে আমি ক্ষমা চেয়ে নিচ্ছি তবে শর্ত একটাই এর পরের ভিডিওতে এই আবাল মাগীর ছাওয়ালদের নিয়ে ভিডিও বানাইলে আরো নিকৃষ্টতর ভাষার ব্যবহার চায় সংগেই আছি এগিয়ে যান👍👍,1,religion
তাহেরি কে জনি সিন্স এর মত কাজ দিতে হবে শালা ফালতু,1,religion
আল্লা সত‍্য আল্লার কোনো শরিক নেই তুই তার চেয়ে বিগ্গানি না তোরে তোর মারে তোর মেয়ে রে এক সাথে চুদবো তোর বাপ তোর ছেলে দেখবে,1,religion
তাহেরী সালা একটা ভন্ড তারে লাথি মেরে স্টেজ থেকে তাড়াবেন দেখবেন এই এলাকায় আর যাবে না।,1,religion
তুই একটা বেদব তাবলিগ নিয়ে কথা বলতে তুই সাহস পাইলি কই বেদবের বাচ্চা তুই কি আমাদের মূর্খ মনে করস,1,religion
আগে জুতা দিয়ে পিটানোর দরকার হল যারা কুত্তার বাচ্চা তাহেরী ভক্ত তাদের,1,religion
বাউন শালা নিজেই গিপদকারি শালা তুই নিজেই হারামি কুওার বাচ্চা,1,religion
শাহরিয়ার কবির খানিক পোলা নাস্তিক কাফের,1,religion
সালা ভন্ড তাহেরি,1,religion
নাস্তিকের বাচ্চা আমি তোরে পাইলে জুতা দিয়া পিটামু,1,religion
কোরআনের ব্যবসা ভালই চলছে আপনারা মাহফিল করেন পরের গীবত করার জন্য আপনারা ইসলামের লোক না কারবালার পন্তরের এজিদের পা চাটা কুকুর।,1,religion
কুত্তার বাচ্চার সাথে এক জন মুমিন বেক্তে,1,religion
তাহসিন ভাই এই দেওয়ানবাগী কাফিরকে আরো বেশি করে রোস্ট করেন সালারা বন্ড ফেরাউন বংশধর ওকে প্রকাশ্যদিবালোকে ফাসি দেওয়ার দাবি জানাচ্ছি সরকারের কাছে তাহসিন ভাই চালিয়ে যান দোয়া রহিলো আপনার প্রতি,1,religion
তুই মাগি তর বাচা অবওস মার জাবে কারন তুই নায় জাইজ জনমা দিচস,1,religion
যারা মাজার কে খারাপ বলে তোরা হইলে জারজ সন্তান,1,religion
এই চ্যানেল ঘুরে আসুন সব ভাল ভাল হুজুরের ওয়াজ ভন্ডের তালিকায় দেয়া। এই চ্যানেলের এডমিন ইহুদিদের দালাল নাস্তিকের বাচ্ছা,1,religion
দেয়ান বাগের জন্ম দিয়েছে কুকুরে,1,religion
শালা মুরগী কবির,1,religion
খানকির পুতেরারে জুতা দিয়া পিটা দেওয়া উচিত,1,religion
ভন্ড দেওয়ান বগিক কুত্তারবাচ্চাকে জুতার বারি দেওয়া উচিত,1,religion
শালার বেটা আগে ভাষা ঠিক কর।ব্যবহার শেখ বেয়াদব,1,religion
জানোআরের বাচ্চা তোরা কী মরবিনা,1,religion
এই শালিকে জুতা দিয়ে পিটাবো,1,religion
কু্ত্তার বাচ্চাদের কে জুতা মারো,1,religion
খানকির পোলা তরে পায়লে পুটিকি দিয়ে আস্ত বাশ ডুকাতাম,1,religion
কুলাঙ্গার সন্তান,1,religion
? শালারে সবাই মিল্লা জুত্তাটা দিয়া পিটায় না কে🤬🤬🤬🤬🤬🤬🖕,1,religion
ফাটফারের বাচ্চা অন্দু চ্যানেল খুলিয়া ফাজলামি করছ,1,religion
এই শালা কুত্তার বাচ্চাদেরকে সামনে পেলে এমন মারতাম যে সারা দুনিয়া মনে রাখত। এইরকম ভনডো মনে হয় আমাদের দেশে নেই।,1,religion
আমার ইচ্ছা করে ওকে জবাই করে কুত্তাদিয়ে খাওয়াতে,1,religion
তাহেরি টা গর্ধব গরু পশু জায়ওয়ান ও জানোওয়ার,1,religion
কবির আর সামিরা কুকুরের পায়খানা,1,religion
এই সুন্নী নাম দিয়ে কিছু ভন্ড মাজার পুজারি বদমাশ ভাদাইম্যা মাথার তার ছেরা বক্তা যেমন ভন্ড আব্বাসি আবুসুফিয়ান তাহেরি আলাউদ্দিন সালেহি এই পাগল ছাগল গুলোকে একসাথে লেংটা করে পাব্লিকের সামনে ছেঁড়া জুতা স্যান্ডেল দিয়ে বারি দেওয়া উচিত ও সাথে পতিতা মহিলার গু খাওয়ানো ফরজ হয়ে গেল ।,1,religion
এ কুত্রার বাচ্ছাদের পা দিয়ে পিসিয়ে মারতে মন চায়।মাদারসোদ,1,religion
ওর পিচে নকিয়া ফোন ডুকাই ব্রাইেবসন করে খালি মিচকল দেয়া হোক।,1,religion
সালাকে জুতা পাটানো হোক,1,religion
ওরে বেটা তুই কাফের,1,religion
কুততার বাচ্চাদের ফাসি চাই,1,religion
সোনসালা এসব খানকিদের ভিডিও ছাড়িসনা,1,religion
জারজ সন্তান সবগুলো ৷ আল্লাহ তোদের বিচার করবে ৷,1,religion
পাগল সালা,1,religion
শালা বেয়াদব,1,religion
মাদার চোদ! কোথাকার ফুটেজ কোথায় লাগাইলি।,1,religion
হালা তোর বাপ কে চাদে দেখছে শালা জারস সনতান,1,religion
ওরে পাইলে কুত্তা দিয়া পুটকি মারাইতাম।,1,religion
এই শালা ও গাজা খাইছে,1,religion
শালা ভন্ড মাদার,1,religion
মাগির পুয়ারে জুতা মারা হোক।,1,religion
এসব দেওয়ান বাগী খানকির পোলারে জুতা মারা উচিৎ।,1,religion
আল্লাহ এই নাস্তিক কে ধ্বংশ করেদেন জানয়ারের বাচ্চা,1,religion
শুয়োরের বাচ্চা,1,religion
কুত্তার বাচ্চা পাক নার বাচ্চা কিয়া মতের লক্ষন।,1,religion
মাগির দালাল,1,religion
দেওয়ান বাগির গূশটি চূদি,1,religion
সে একদিন কুত্তার মত মরবে,1,religion
কুত্তার বাচ্চার ফাঁসি চাই 😈😈😈😈😠😠😠😠😠😡😡😡😡,1,religion
মিজান আজহারী জারজ,1,religion
তরে কুত্তা দিয়া সুদানি দরকার হালা গাজাকোর,1,religion
তর মারে চুদি,1,religion
কিরে ফকিরন্নির পুত।তোর জন্মের ঠিক আছে।সালা হারামজাদা,1,religion
ওটা তোর বাবার কুত্তার বাচ্চার তুরা আমার আল্লার কুরআনে উপোর চোটি রেখে ছিশ তোকে আমার আল্লাহ আগুনে পুরাবে আমি সেটায় চাই বন্ধর ওর ফাশি দেয়ে দাও আমার নবির কুরআনকে ছোটো করছে আল্লাহ জানো ওদের চোখ মুখ হাত কানা করে দাও সকল ভাই বোন বলেন আমিন,1,religion
ঐ মাগীর পোলা আগে বয়ান শুন কি বলে,1,religion
তাহেরি হলো বিশ্বের ভন্ড ওই হলো একটি পাগল ওর মতো বেধফ আমাদের বাংলাদেশ নাই,1,religion
অভার বালপাকনামী চুদাও। মাদারচুদের বাচ্চা তোর বয়স কত?,1,religion
এই শালা নাস্তিক ভন্ড কে জুতা পেটা করে মহফিল থেকে বের দিয়ে জুতার মালা গলায় দেওয়া উচিত আমার বাড়ী সিলেটে মাজার এর শাহজালাল মাজার এর পাশে আমার নিজের চোখে দেখা মাজার এর পশ্চিম পাশে কয়েকটা ভন্ড লাল কাপড় পরে বসে থাকে গাঁজা নিয়ে ওরা খায় এবং বিক্রি ও করে আমি নিজেই দেখেছি এরকম আরও পাওয়া যায় শাহপরান মাজারের পাশেও এজন্য আমি হুজুরের কথায় একমত আছি,1,religion
তরে থাপ্পড় দিয়ে টেস থেকে নামা হারামজাদা,1,religion
দেওয়ানবাগীর জন্মের ঠিক নাই । এই দেওয়ানমাগী একটা মাদারচুত। যারা দিছে তারা সবটি মাদা ত । একটা লাইক দেওয়া মানে দেওয়নবাগীর পু কি দিয়ে ট্রেন ডুকানোর সমান।,1,religion
মাদারসুদ রা মাজারি পূজা বলবি কেন? আল্লাহ ধর্ম উনাদের দ্বারাইতো প্রচার হয়ছে এবং আমরা ইসলাম ধর্ম পেয়েছি।,1,religion
শালায় কেমনে পাকনা পাকনা কথা বলে,1,religion
খবিশ মাজার পূজারী ইবলিশ শয়তান মুনাফিক রাবিশ বাস্টার্ড এই খবিশের মুখ দেখলে ঘৃনা করে,1,religion
কুত্তার বাচ্চা ভন্ড।,1,religion
ওই হালায় ভনড,1,religion
তাহেরী শালা বদমাইশ,1,religion
তুই খবিস সালা,1,religion
এই বাটপার কে ওয়াজের মঞ্চে উঠাইছে কোন সালারা। বয়সে এখন নাকের ময়লা যায় কে উঠাইছে এই বেয়াদব কে।??? সাবধান হইয়া যাও। সবাই,1,religion
দেযাওয়ান বাগি একটা পুটকা মাছ,1,religion
এই পাগলদের কে দেশ থেকে বাহির করা উচৎ,1,religion
ছাগলের বাচ্ছারা মন চায় জুতা দিয়া পিটাই।,1,religion
ভন্ড সালার মুরিদ😑,1,religion
তুই কি বুজবিরে মাগির পুত,1,religion
ওই কুত্তার বাচ্চাদের লাথি মেরে চেয়ার থেকে ফেলে দেওয়া উচিত ওরা চেয়ারে বসার যোগ্য না,1,religion
এই রকম বেপর্দা মাগী নাস্তিক এর অনুষ্ঠানে না যাওয়াই ভালো,1,religion
অই বেড তুই এক নাম্বার বন্ড সালা।লেখা পডা কত টকু পডছো। বেডা আমেন হয়াগেছে হে,1,religion
শালা ভন্ড এইদেওয়ান বাগিরে মাইরা লা,1,religion
তাহেরি মাদা্রচোদ জোদি আমির হামযা কে নিয়া কিছু বলে তা হলে আর জিব্বা কেটে দিমু শালার,1,religion
চার নাস্তিকের মায়েরে আমি,1,religion
মাগী টাও হুজুরকে কথা বলতে দেয় নাই।,1,religion
আরেকজনকে অপমান করার আগে নিজের কথা একবার ভাব মাদারচোদ,1,religion
মোসলেমানের দেশে নাস্তিক একজন আলেম নিয়ে টকশো।।,1,religion
মিজানুর রহমান আযহারী খুব ভালো ব্যাক্তি ওনার কতা শুনলে কলিজা টা ঠান্ডা হয়ে যাই উনাকে জে কাফের বলে সে তো নাম্বার ওয়ান কুত্তা আর তাহিরি ত । নাম্বার বন্ড,1,religion
মাদারচোদ তোর মারে কুত্তা দিয়ে চোদা দরকার খানকি মাগির পোলা।,1,religion
তুই আলেম নামের জানুয়ার,1,religion
বাংলাদেশের মানুষ এতই কি পোকা যার তার কথা বিশ্বাস করে ফেলে আরে ওখানে তো কোরআনের বাংলা অনুবাদ কি পাওয়া যায় না পড়ে দেখতে পারে না যতই মানুষ বিশ্বাস করবে তত এইসব ভন্ড লোকের আবির্ভাব ঘটবে শালা কুত্তার বাচ্চা এদেরকে কুত্তা কুত্তা কে অসম্মান করা হবে কারণ সেও আল্লাহর বানানো একটা জীব যে তার মালিককে ভয় পায় কিন্তু এত পায় না,1,religion
হাচিনা ভারতের দালাল আর ওর অনুসারিরাও সবগুলা দালাল সালারা ইছলামিক দেস বাংলাদেশে কোনো মুরতি থাকতে দেয়াহবেনা এটাই ঠিক,1,religion
কমিটির শালায় মানুষ না কুত্তালীগ,1,religion
আরে কুত্তার বাচ্চা সময় থাকতে ভালো হয়ে যা,1,religion
এই বেইমান কুত্তার বাচ্চা নাফরমান৷তরে কুত্তা দিয়ে জন্ম দিছে তাই এ কথা বলস৷ইহুদির বাচ্চা৷তুই তো ইহুদি তাই আমাদের মুসলমানদের ইমান নষ্ট করার জন্য এ কথা বল৷এ কুত্তার বাচ্চা তুই পুরাটা ওয়াজ শুন আগে তারপর বল কি বলছে৷বুজে শুনে ভিডিও পোস্ট দিবি কুত্তা৷,1,religion
দেওয়ানবাগীর পাছায় চড় থাপ্পর ইল্ডা,1,religion
তুই কুত্তা,1,religion
তাহেরির কন্ঠ সুন্দর কিন্তু শালা যে চরম ভন্ড দেখলে থাপরাইতে ইচ্ছা করে,1,religion
তদের মতন শিশু মাওলানার দরকারনাই শালা অলি আউলিয়ার দুশমনরা,1,religion
শাহরিয়া কবিরকে ফাঁসি চাই শুকরের বাচ্ছা।,1,religion
মন থেকে আপনাকে ধন্যবাদ ভাই। এই কুত্তাবাগীর উপর লানত পরুক। 😑,1,religion
এই মাদারচোদ কেমনে সুস্থ আছে এ মুসলমানদের দেশে কারা পিছনে আছে?? বোকা চোদারা আবার এই জারজের কাছে যায়,1,religion
এ দেওয়ানমাগীকে পুড়িয়ে মারতে পারলে মনটা শান্তিপেত।,1,religion
সালা হারামির বাচ্চা তুই উজানির ময়দান ঝাড়ু দেয়ার জগ্যতাও তর হয় নাই ছাগল,1,religion
জানুয়ার এরা,1,religion
ঝা বেটা ।চুলের সুন্নত কি আরো আবাল কি বলে।। সালায় ফাওল একটা,1,religion
কুত্তার বাইচারা,1,religion
উপস্থাপিকার একটা বেয়াদব কুলাঙ্গার নাস্তিক,1,religion
ভন্ড সালারে ফাইলে খুন করব,1,religion
এই শালাকে বাস্তবে বলার পড়ো বলে আমি গান করি নাই আল্লাহ আল্লাহ করছি,1,religion
বেইমানের বাচ্চারা ফিজুর রহমান সিদ্দিকী কি চিনেনা তার ছেড়া কুত্তা কথাগুলো ভালো করে বোঝো,1,religion
তাকে কুত্তা দিয়ে চুদানু দরকার,1,religion
বাল পাকনারে আমার কাছে পাইলে দুইটা থাপর দিতাম,1,religion
আল্লাহ অর উপর ঠাডা ফালাও কুত্তার বাচ্চা,1,religion
খানকির পোলা সাহাবীরা চুল কামাইছেন,1,religion
লাটি লইয়া কি রকম জীকির। এই বেটা তুই ঐসব জীকির কোথায় পেলি। হালার পু হালা।তরে যে কি বলে আর কোন ভাষায় গালি দিব। আমি কোন ভাষাই খুজে পাইচ্ছি না।তর মায় যে তকে জন্ম দিয়ে কি ভূল করছে।,1,religion
মাদারচুত,1,religion
এ হারামি দের মুখে জুতা মারি।,1,religion
বন্দরের না দেখাইয়া যদি একটা কুত্তারা দেখাতেন খুশি হইতাম দেওয়ানবাগী হেল বন্দরের না দেখাইয়া একটা কুত্তার দেখাতেন তাও ভালো হতো,1,religion
আসসালামু আলাইকুম ভাইয়া ভিডিওটা অনেক ভালো লাগলো বাট আফসোস এতোটুকুই রয়ে গেল এই সব কুত্তার বাচ্চাদের জুতা দিয়ে পিঠাতে পারলাম না😰😰😰,1,religion
নুনুর গোড়ায় এখনো এক গোছা বাল উঠেনি চুদির্ভাই আরেকজনের পুটকি মারতে আসো। বান্দিরপুত মিনিটের ওয়াজে এক লাইন কোরানের আয়াত পাইলাম না। নিজের তো লেখাপড়া করিসই নি আবার ওয়াজ চুদাইতেছিস। মাগীরপুত তোর ফেসবুক লাগে কি জন্যরে?,1,religion
খানকির বাচ্চা!!!! শরীয়া আর অসাম্প্রদায়িকতা কী আলাদা জিনিস নাস্তিক মাগির বাচ্চা।,1,religion
তুই নিজেই ত বন্ড শালা,1,religion
জুতা মার শালা কাপের দের,1,religion
কুওার বাচ্চারে পাইলে জুতা দিয়া পিটাতাম সালা তোর দাড়ি আছেনি খানকির পুলা,1,religion
বেয়াদবের বাচ্চাকে দেশ থেকে বের করা হোক মাদারচোদকে,1,religion
খাজা বাবার ফুটকি বাইদি ডুকাইবো বরুয়া বাঁশ। আর তুই সুদাই রে খাজা বাবার লোক্।খাজা বাবা যে সে তার হিসাব দিয়া শেষ করতে পারেন নি তা দেখ।,1,religion
সালা ভাই তোমার লম্বা চুলের দলিল কোথায় ?,1,religion
হানকির পুলা তুই কে এইসব বলার তুই ভালো কিছু প্রচার কর ভালো মায়ের সন্তান হলে তুই জারজ,1,religion
তরে লেংটা কইরা পিটামো মাদারচোদ কাপের,1,religion
এই কুত্তার বাচ্চারা জারজ তাই এই রকম।,1,religion
এই সালা হছে কুত্তার তিন নম্বর বাচ্চা,1,religion
দেওয়ানবাগীর মায়রে চুদি বোনরে চুদি ইন্ডিয়া জাইয়া,1,religion
সালা মাদার চোদ,1,religion
এদের বাপ না থাকায় জনম এরাজরোস সনত্মান,1,religion
গঞ্জিকা সেবন বেশি হয়ে গেছে হালাগো,1,religion
মিজানুর রহমান সাহেব যে বলছে রাসুল সা নাকি ছাগলের চামড়া খেয়েছিল এইটা উনি কি বলছেন উত্তর দিন। আপনি হইলেন আরেকটি দালাল। মিজানুর রহমান হইছে ডিজিটাল ভন্ড বক্তা।,1,religion
শালা আমাদের জেলার বদনাম করতাচে হিজরা গুলা বইসা রইচে,1,religion
কোরানে কোন জায়গায় লাফাইতে বলেছে?উ আ করতে বলেছে? ছাগলা তাহেরী!,1,religion
এই মাগি তোকে চুদেছে না কি তোর মা কে চুদেছে তায়েরি কুকুরের বাচ্চারা ইসলামকে নষ্ট করিস,1,religion
জারজের বাচ্চারা তোরা নাস্তিক না তুমি তোরা ইসলাম বিদ্বেষী আমাদের কলিজার মধ্যে আগুন লাগিয়েছিস তোদের জন্য এখন থেকে হেদায়েতের দোয়া করব না তারপরও বলি আল্লাহ তাদের নসিবে রাখলে আলহামদুলিল্লাহ আর না রাখলে আল্লাহ যাতে তোদের বিচার এই দুনিয়াতে করে আখিরাতে করে দুনিয়ার সর্ব নিকৃষ্ট স্থান জাহান্নামে নিম্ন স্থানে তোদেরকে রাখে আল্লাহুম্মা আমীন। মাসুদ কোরআনকে অবমাননা করেছিস হৃদয়ের মধ্যে কোরআন ঘাট আছে প্রত্যেক কোরআনের হাফেজ এর মধ্যে কোরআন গাথা আছে আমার প্রিয় নবী মুহাম্মদ সাল্লাল্লাহু আলাইহি ওয়া সাল্লাম এর হৃদয়ের মধ্য গাঁথা ছিল তা থেকে কিভাবে ছিনিয়ে নিবি তুই ইসলাম আছে ছিল থাকবে যে তাকে ধ্বংস করতে চাইবে সে নিজেই ধ্বংস হবে ইনশাআল্লাহ।,1,religion
সালা কুকুরের বাচ্চা তুই ভন্ড চুল ছোট করা হারাম তরে কে কইছে,1,religion
ওয়াজ করবে ভাল কথা এই দল আর ওই দল কি?? ঔই হালার ফুত,1,religion
আরে কাফেরের বাচ্চারা মাথা যদি নতো করতে হয় তাহলে একজনের সামনে করবো সে হলো আমার আল্লা রব্বুল আলামীনের সামনে করবো আল্লা তুমি এদের হেদায়েত দান করো আর না হলে এই শয়তান দের দুনিয়ার থেকে তুলে নাও আমিন,1,religion
হে কি বালের মুফতি কুরআনের কোন আয়াত জানে কিনা সন্দেহ হয় খালি জিকির আর কিচ্ছা কাহিনী কোন আয়াত নাই কোন হাদিসের রেফারেন্স নাই হালায় কয় উহুদের ময়দানে নবীজীর দন্ত মোবারাক হইছে এইডা পুরাই মিথ্যা কথা যেখানে দন্ত মোবারাক হইছে আমি নিজের চোখে দেখে আইছি শালা মিথ্যাবাদী ছাগল তাহেরী ফালতু,1,religion
পিটা দে শালারে,1,religion
বেশ্যার চোদা তাহেরি,1,religion
নাস্তিক গুলাকে জুতা পিটানো হোক।,1,religion
এই খানকির পোলা দেওয়ানবাগী কে যারা গু মেখে জুতা মারতে চান তারা একটা করে কমেন্ট করে জান প্লিজ,1,religion
হালার পুতে পুরাই ভন্ড,1,religion
হালার মাথায় কিতা বাল রাখছেনি গাজাখুর,1,religion
আল্লাহ না করুক হা হা হা কুত্তি নাস্তি হয়ে আস্তিক বিশ্বাস করস,1,religion
এই হারামি ছোট বক্তাগুলো পরিহার করুন।,1,religion
তোর আহলে খবিসের বাচ্চা তুই কোন বালের দলে আছিস বল কানখির পুলা।।সব আলেমকে কোন মূখে ভন্ড বলছিস মাগির পুলা।।,1,religion
জুতাদি পিটাও তাহেরিকে,1,religion
এই শালা তর বয়স কতো????,1,religion
খানকিমাগী তুই কি বুঝিস তুই এত কথা বলিস কেন তোর আজাইরা ভিডিও শুনতে আর ভালো লাগেনা মাগির গড়ের মাগী,1,religion
তুই নিজেও একটা কুলাজ্ঞার মাদারী,1,religion
ভন্ড ছুদা,1,religion
লোপা খানকিরে পিছা দিয়া পিটান হবে কে কে রাজি আছেন,1,religion
মাদারী গাঁজা খোর মাগীখোর।,1,religion
জুতামার সালারে কুত্তার বাচ্চা,1,religion
কুকুরের মত ভাষা রাসুলের সুন্নত না কি ? বডি লেঙ্গুয়েজ পাগলা কুকুরের মতো কেন? বিধর্মীরা তোমাদের দেখলে হাসে বলে ইসলাম ধর্ম উন্মাদের পাগলের ধর্ম ?,1,religion
শালারা জারাখুর টেইজেকেনভশে লেংটারপাগল,1,religion
যারজ সন্তান এতিখানায় লেখাপড়া করে একটু বেশি যে মন তুই,1,religion
আসছে অনেক রকমের খানকি দেখাযাচছে,1,religion
তুই তাহেরির চোদা মাদার পূজারি তোর মায়রে চুদি,1,religion
ভন্ড পীর দেওয়ান বাগী কে আমি সপ্ননে দেখছি কিন্তু সকালে উঠে দেখি কাপুর ভিজা ? সালার গোয়া দিয়া গড়ম রট দিমু,1,religion
আল্লামা মুমিনুল হক যেখানে বসে আছেন আমি যদি ওইখানে থাকতাম তাহলে ওইখানে দাড়িয়ে চারজন নাস্তিকের মুখের ওপরে সিরিয়ালে প্রস্রাব করতাম,1,religion
নাস্তিকের বাচ্চা নাস্তিক চোরের বাচ্চা মুরগী চোর।,1,religion
শেয়ার করে নাস্তিক দের দেখাব নাকি? শালা এসব প্রচার তুই করছিস কেন? অদের ফেমাস করে দিচ্ছস তোরাই।,1,religion
ওই দেয়া কুত্তা গুলির সামনে আনাইয়া থাবড়া নো উচিত 😁😁😁,1,religion
খানকির ছেকে তোকে পেলে জে কি কোরবো,1,religion
জিহাদি কুকুর টার ওয়াজ এর খবর দিলে খুশি হবো ওরে একটা জুওা দিয়া মারতে চাই বুশ রে যে ভাবে মেরে ছিলো,1,religion
খবিস গরু ছাগল পিটানো দরকার,1,religion
কুত্তার বাচ্চাদের ফাসি ফাশি চাই।,1,religion
নাস্তিকের বাচ্চা গুলোর গোফ দেখেছেন ????,1,religion
সালা তুই তো বড় শয়তান ভন্ড কোথার কুকুরের বাচ্ছা,1,religion
কুরানের মাহফিল যে বাধা দে তারা হলে সয়তানের জারজ সন্তান যে মাজার পুজারি সে নাস্তিক সালারপুতে মাজার পুজারি,1,religion
তুই কোনকার ভালো মানুষ বাইনচুদ,1,religion
দেওয়ান মাগি 😂,1,religion
সালার পুত তুর মারে ছুদি একজন দিনদার আলেম কে নিয়ে একটা মিথ্যা কথা লিখেছচ তুই একজন মুনাফেক ইহুদির দালাল,1,religion
কুলাংগার এর বাচ্চা তোর জন্য জাহান্নামের আগুন অপেক্ষায় আছে শুধু তোর মৃত্যু তা জন্য অপেক্ষা মনে রাখিস কুত্তার বাচ্চা তোরে আল্লাহ কেমন শাস্তি দেয়,1,religion
করা মানুষ গুলো কুত্তার জন্মের,1,religion
ফরজের খবর নাই ছুন্নাত চোদায় ভন্ড মাদার চোদ,1,religion
শালা কটা বাইনচুদ,1,religion
ওই খানকি মাগিও নাচতিক,1,religion
প্লিজ প্লিজ প্লিজ কেউ দেওয়ান বাগীকে চুদে দিন যত কন্ডম লাগবে আমি আপনাদেরকে বিমানে করে পাঠিয়ে দিবো ।,1,religion
ভাইয়া একে কুত্তা বললে কুত্তা ছোটো করা চরম অপমান ও হবে,1,religion
কুরান ত্রকটা গুদের বই বালের ধর্ম,1,religion
ছিত করি হালাই হেতের দানা দুগা চেঁচি দিলে টিক হয় যায়বো।,1,religion
এই খানকির বাচ্চা গুলারে আগুনে পুরিয়ে মারা দরকার?,1,religion
আবার কোন আবাল রা দেয়।,1,religion
চালা ভড,1,religion
ভন্ড তর মারে চুদি,1,religion
তুমি একটা রাম ছাগাল কারণ তোমার কোন কোরআন হাদিসের শিক্ষা নাই তুমি অন্য আলেমের ভুল ধরছ আবার বললাম ছাগল।,1,religion
চার কুত্তার বাচ্চা নাস্তিক গুলিই কে জুতাদিয়া বাড়িয়াইতে হবে লেংটাকরে।,1,religion
বালপাকনা বক্তা!,1,religion
এই সালা আরেক বাটপার কয় কি,1,religion
শুকুরের বাচ্চা,1,religion
মিজানুর রহমানের শয়তানের বাচ্চা ভন্ড ভন্ড,1,religion
চুরের বাচ্চার মিথ্যা বলে ভিও বাড়াবি এই রকম কাজ করে যারা তাদের জন্মের ঠিক নাই,1,religion
কুত্তা আর এক কুত্তি পুরাই পাগল হয়ে গেছে,1,religion
দেওয়ানবাগির ওখানে আমি যখন প্রথম দিন যাই ওই দিনি আমি বুঝেছি এটা ভন্ড এটা শিরক এটা কপটতা করার প্রন্থা😂😂😂😂😂😂মহিলাদরর গায়ে হাত দেয় লুইচ্চা আবার আমাকে নবি রাসুলের ছবি ও দেখাইছিলো😁😁😁😁😁😁বিশ্বাস করানোর জন্যে একটা ছাগল,1,religion
এই মাগিৰ ফুয়া তৰ মা ৰে ছুদি খানকীৰ ফুয়া,1,religion
নাস্তিকরা কুকুরের শুকরের থেকেও নিক্কৃষ্ট। কোরআনের কথা।,1,religion
সাঈদীকে চাঁদে দেখা যায় দেওয়ান মাদারিকে দেখা যায় 😂,1,religion
একটা মাগি তিনটা মাগির দালাল,1,religion
কুত্তার বাচ্চারে ধইরা মাইরালা বাচ্চা সত্য কথা বলতো এই জন্য এই অবস্থা না হুজুর সাহেব সত্যি কথা বলছি,1,religion
জানোয়ারের বাচ্চা কুত্তা নাস্তিক,1,religion
টা কুকুরে বাচ্চা কুকুরে বাচ্চাকে জুতা মারবেন কেকে,1,religion
সালা পেট ফাইট্টা মরবো৷ সালা যদি নবীদের আমলে জম্ম নেয় ৷তাহলে এই পেটুকের বয়স কত????? হায়রে মানুষ সত্য মিথ্যা কিছুই বোঝেনা৷,1,religion
তারা চারজন জারজ সনতান তাই এসব কথা বলে আললাহর গজব নাজিল করন,1,religion
সালারে কোন মাদারচোদ ওয়াজ শিকাইছে করুনচোদ ওয়াজ।😂😂😂😂😂,1,religion
কুকুর দেয়ান বাগি তার একটা ছেলে ও দেখেছি কুকু এর বাচ্চা তাদের কি করার দরকার পিটা মারার দরকার কুকুর আর বাচ্চা গুলু কুকুর আরো আছে তাহেরী,1,religion
কুত্তার বাচ্চা ভন্ড তাহেরীর কতল করা উচিত এ মাল মুরতাদ হয়ে গেছে ইসলামের ক্ষতি করছে জেকের এই ভবে করে পাগল মাল,1,religion
তাহেরিকে জুতা পিটা করা দরকার,1,religion
শালা ভণ্ড বিদাতি গাজাখুর নাচ গান ছেড়ে সঠিক জিকির কর না হলে 👞 👡 👢 দিয়ে তরে ঠিক করমু,1,religion
যে বয়সে বাচ্চারা পড়াশোনা করতে যায় সেই বয়সে এই মালটা গাঁড় পাকা হয়েগেছে । এগুলো শুধু মাত্র ইসলামে সম্ভব ।,1,religion
তাহেরি তরে পুটকি মারছে নাকি,1,religion
সালিটা বড় নাস্তিক,1,religion
চারটা ই নাস্তিক,1,religion
এই সালারা হল ইহুদি দের দালাল,1,religion
যে গান করছে সে একটা মাগি,1,religion
সালারপুতে নাস্তিক,1,religion
সাবাস ভাই এই কুত্তার বাচ্চাগোরে নিয়া ভিডিও বানাইছেন।,1,religion
দেখেন তুমারে কুত্তার বাচ্ছার মত দেওয়ান ছাগির বাচ্চা,1,religion
খানকির পুত অগল,1,religion
হের মার চুদ,1,religion
নাস্তিক মাগির পলা গের পাইলে বুঝাই দিতাম,1,religion
একটা বানচুদ সালা,1,religion
তুইন আরেক নয়া পাগল ভারইছত মাদারচুত,1,religion
চার শুয়োরের বাচ্চা জন মুসলিম হয় কি করে কথা,1,religion
এসব ভন্ডদের পাছায় গরম করে লোহার রড ডুকাই দেওয়াই বেটার 😠 আর ডিসলাইক দেই কে এসব 😡,1,religion
এই মালাউন এর বাচ্চা দনদটা লাগাইছে ওয়াজ এর মধ্যে শালার পুতে মালাউন এর বাচ্চায় আলোচনা আর খুইজজা পায়না শাহজালাল মাজারে কোন পাগলে গাঞ্জা খায় এইগুলা কি তর আলোচনা নাকি কুরআন সুননার আলোচনা করতে আইচস আসলে তুই অলির বিপক্ষে কেমনে কথা বলবি সেই লাইন করতাসস না এখন গেনজাম লাগাইয়া এই মালাউন এর দালাল কুরআন তেলাওয়াত পরে তর তেলাওয়াত আল্লাহর দরবারে কবুল হবেনা কারণ তুই নবী ও অলির দুশমন আল্লাহ এই সব নবীর দুশমন অলির দুশমন বক্তা থেকে আমাদের সাবধান হওয়ার তৌফিক দান কর।,1,religion
হুজুর চুলগুলি আর একটু লম্বা হলে ভালো হতো।শালা বানদর্ চুলের বিষয়ে আবার ফতোয়া দেয়।এদের জুতা পিটা করা দরকার।,1,religion
সালার বাবা কয়টা??? মারালি বাবা জারালি বাবা মুতখোর বাবা বোকাচুদা বাবা যেগুলা বসে আছে সবার পাছা দিয়া গরম আগন ভরতে হবে। সালার ভন্ডর বাচ্চারা।,1,religion
হুজুর সব কথা গুলো ঠিক বলেছেন আপনি ঠিক আছেন ঐ সালা কে জুতা দিয়ে পিটানো উচিত,1,religion
ভন্দ তাহেরী কোথাকার থাপরাইতে মন চায় সালা চোর,1,religion
তবে মায়ের যে মেয়েটা কথা বলতেছে উনাকে মাথার চুল দিশা ইচ্ছা আলগা তালা গায়ে দেওয়ার দরকার কারণ উনি একটা ইসলামের বিষয় নিয়ে কথা বলতেছে ইহুদির বাচ্চা,1,religion
সালার পুত,1,religion
শতো শতো মানুষ কমেন্ট করছে জানোয়ারের বাচ্চা কেউ তো তোরে ভালো কইলো না৷ জানোয়ার,1,religion
নাস্তিক দের জুতা পিটা করা দরকার,1,religion
তুর গুষ্টির মারে বাপ অমানুষ কুত্তা জারচ সন্তান বন্ড জুতা মার তালে তালে তালে,1,religion
এই কুকুরের আবার কবে জম্ম হ‌য়ছে বাংলাদেশে যত দিন এই কুকুরেরা ঘেউ ঘেউ করবে ততদিন মানুষ অন্ধ অনুসরণ ছাড়া আর কিছুই শিখতে পারবে না,1,religion
তরে পাইলে চুদে চার নাম্বার বাচ্চা দিতাম শালি মাগি?????,1,religion
সাশালা শুয়োর তুই কি জানিস,1,religion
যা তুই যাইয়া কারাবন কাতিবিন হোগায় গরম রোদ ঢুকাইয়া দিবে,1,religion
এটা মাগী না অন্য কিছু মামুনুল হুজুর আপনি এদের সাথে কেন কথা বলেন এই চারজন অনেক বড় নাস্তিক কুকুরের বাচ্চা জানোয়ারের বাচ্চা ইহুদিদের বাচ্চা,1,religion
তুই তো শালা গাটটি তুই কি বুঝবি মাজার কি জিনিস,1,religion
দেওয়ান বাগি হলো সব বন্ড়ের বাপ মাদারি রে সবাইর সামনে জবাই করে দিলে,1,religion
শয়তান হারামজাদা,1,religion
এই বাচ্চা হুজুরে মা রে আমি চুদি মাদার,1,religion
এই শালি পতিতা,1,religion
তোর বয়স হয়ছে ওয়াজ করার তুই এতো বালপাকনা কেন বেয়াদব,1,religion
নাউজুবিলা নটির পোলারে জবাই কড়া উচিত,1,religion
শুয়োরের বাচ্চা ভন্ড তাহির,1,religion
খানকির পোলা ভুয়া শিরোনাম দিছোছ কেন,1,religion
খানকী মাগী আর নাস্তিক,1,religion
কুত্তার বাচ্চা গুলো কি মরবে না আর ফাজিল মহিলা তো উপস্থাপিকা না নাস্তিক এর দালাল,1,religion
মাঝখানে এই শাউয়ার বেডি কেডা,1,religion
দেওয়ানবাগী সালারে সামনে পাইলে সালমানের পায়খানা ইচ্ছা মতো খাওয়াইতাম।,1,religion
দেওয়ান খানকি মাগি চুতমারানি চুদলাম নাহ,1,religion
শাহরিয়ার কবির মুরগি চোর সালা খানকির পোলা,1,religion
অল্প বয়সেই গিফত গাওয়া আরমব করছে বাল বাচ্চা,1,religion
শালা বাইনচুদ তুই বড় বন্ডা খালেদ সাইফুল্লাহ বন্ড নাকি শালা তরে পাইলে জুতা পিটা করতাম,1,religion
এই চার কুত্তারবাচ্চা কে জুতা দিয়া পিঠাতে হবে,1,religion
কিন্তু তোর চুল কত বড় সালা ভন্ড কুক্তার বাচ্ছা,1,religion
খানকির বাচচাকে জবাব করন,1,religion
সালা ভন্ড ফুটকামাছ তরে জুতাদি বাইরায়বো জনগন সামনে পাইলে সবাই রাজি হালারে জুতামারতে,1,religion
আব্বাসি যদি মাজার পুজারি না হয় তুই জারজ।,1,religion
ভন্ড সালার মারে আমি গোয়াল ঘরে দেখছি ?,1,religion
শালা তুই বেয়াদব,1,religion
দেয়ানবাগী শুওরের বাচ্চা কে কাপড় খুলে মারা উচিৎ। সরকারের উচিৎ ব্যবস্থা নেয়া উচিৎ।,1,religion
এটা তো একটা ছাগলের বাচ্চা,1,religion
দেওয়ানবাগী রে জুতা দিয়া পিডাইয়া শুয়োরের বাচ্চা,1,religion
ওই সালা চোর,1,religion
দেওয়ান বাগী এ কি একটা পাগলা চুদা তোল ওর নামা স্টেজ থেকে,1,religion
সালা একটা বনড সালার নুনু কেটে দেওয়া হোক,1,religion
মুরগিচোর শাহরিয়ার কবির জারজ সন্তান শুয়োরের বাচ্চা,1,religion
মাদারী অামীর হামজা নবীর দোষমন মাদরী চোদ,1,religion
কুত্তার বাচ্চা তাহেরি,1,religion
খানকির পোলারে জুতা কে কে মারবেন আমার সাথে সারা দিন,1,religion
সালারে গুয়ামারমো,1,religion
এই ইহুদী খৃস্টান আর বাচ্চাদেরকে মুসলমানের দেশে থাকতে দেওয়া যাবে না ওদেরকে গলায় জুতার মালা দিয়ে তাড়িয়ে দেওয়া দরকার,1,religion
কুত্তার বাচ্চাকেক জব কর,1,religion
এই কুতার বাচ্ছা,1,religion
সালা কুত্তা,1,religion
ভাই তুই ঠিক আছোস তো?তোর মুখে দাড়ি টুপি কই তুই তো মালাউন এর বাচ্চা প্রতারক কথা কাজে মিল নেই মুকাফেক তুই পিকচার এ দিলি হাফিজুর রহমান এর পিকচার কিন্তু ভিডিও তে প্রুফ দিলি কই ? সালার চ্যানেলে সবাই রিপোর্ট মারো,1,religion
ভন্ড দেওয়ানবাগীর চুদাদে ভন্ড দেওয়ানবাগীর একটা মাগির পো,1,religion
কুদাল বাবা ছাগল বাবা ফতেঃ বাবা গুড়া বাবা মহিষ বাবা হায়রে ছাগল🐐 বাবা,1,religion
শালা গিয়াসউদ্দিন তাহেরী হলো আসল শালা পুরো ভন্ড,1,religion
এই হারামজাদা কি জানে কি বলে,1,religion
এ শালা ভন্ড মোল্লা।,1,religion
ছাগলের পেট থেকে এই চারটা এক সাথেই বের হয়েছে ওরা ছোট বেলায় মক্তবে ও পড়েনি,1,religion
মুরগি কবির তোরে চুদবাম রে👎🔫,1,religion
মুসলিম এক আল্লার গোলাম কোন হূহদী মুনাফিক কুওার বাচ্চার কছে মাথা নত করে নি একমাএ আল্লাহ ছাড়া,1,religion
এই দেওয়া বন্ড কুতারমুখে আট বছরের জারুক দিয়ে মারদিতে হবে আর য়ারা বক্ত আছে তাদেরকে জুতাদিয়ে মুখে মারতে হবে মুনাফিক রেদল সবাই ঢাকার মতিঝিলে পড়ে আছে কি,1,religion
এসব হল ভন্ডামি এইসব মাদারচোদেরা জুতা দিয়া বাইরাইয়া দেশ থেকে তাড়ানো উচিত,1,religion
আল্লাহর বন্ধুকে গালি দিতে আপনাদের বিবেকে বাধে না। শয়তান তাসকিন যে কুত্তার থেখেও অধম যে ইউটুবে এ টা অপপ্রচার করে লাখ লাখ টাকা ইনকাম করছে। এ কুলাঙ্গার কে কেউ গালি দেয় না। হায়রে বাংলার শিক্ষিত মানুষ হায়রে এদের বিবেক ।,1,religion
তুমি অনেক সুন্দর আল্লাহর ধন মাটি থেকে আসমান পর্যন্ত।তোমার মাং ফেটে চূর্ন বি চূর্ন হয়ে গিয়েছিল। আর বাকি ধনের অংশ তোমার মার মাং ফাটিয়ে দিয়ে তোমার বাবার গোয়ার ভিতরে যিয়ে বাকিটা ধন তর পুর বংশের মাং ফাটিয়ে তর মুখ দিয়ে ঢুকিয়ে তর পাইখানার দরজা দিয়ে বের করেছ।তর এই তিন যায়গায় ধন ঢোকার কারণে তর মাং গোয়ার ছিদু এবং মুখ দিয়ে ঢোকার কারণে তর শরীর মালের ভরে তর পোর শরীর ফেটে মাং হার গোল হাওয়া হয়ে যায়।তার পর তোকে জাহান্নামের সপ্তম কোপে নিখেপ করে। সেখানে তোকে আগুনের হোল দারা চোদায়ছে। এভাবেই আ জনম জাহান্নামের তোকে চোদা দিতে হবে আরো কঠোর আজাব দিবে।তবু তর জিন দিগি শেষ হবে না।এ কথায় আজীবন জাহান্নামে থাকবি নটির চোদা তুই,1,religion
খানকি মাগী পক্ষ নিয়ে উপস্থাপনা করে। ওর ভোদায় রড ঢুকানো দরকার।,1,religion
শালা ভন্ডর গান ভালোই আছে। এর কপালে সব মুসলমানের জুতা,1,religion
এই সব মাগির বাচ্চা পির গুলারে জবাই করা উচিত,1,religion
আই তোকেচুদি তোরগূদের,1,religion
এমাগি আবার কি কয় দেওয়ানবাগীর ভিতরে নাকি আল্লাহ মাগির দুই দুই উরুর চিপায় দিয়ে মরিচ দাও,1,religion
খাংকি মাগি তুই মুসলিম নাকি,1,religion
মাদারচুদ তোরে জুতা দিয়া বারাইয়া ঠিক করার দরকার।,1,religion
ভন্ড কমেডি তাহেরিকে জুতার বাড়ি মারতে হবে।। কয়েকবার খাইছে শালা জুতার বাড়ি। তবুও শরম হয়না তার,1,religion
ট্যাপা মাছের মতো পেট মাদারচোদ দেওয়ান মাগির কষ্ট লাগে তাদের জন্য যারা ভন্ডর কথা গুলো বিশ্বাস করে শুনছে।।।,1,religion
মাদারছোদ কিসের শিশু তক্তা তাহেরি সম্পকে কি কথা বলে তহেরি নবীকে ভাল বাসে তুই মাদার চোদ দুসমনে রাসুল খানকিরপোলা তোরে যে দাওয়াত দিছে হেতে মাদারচৌদ,1,religion
সালা কাফের,1,religion
একটাকুউতারবাইচা।তরজনমেরটিকনাই।সুউরের।জনমহয়েচে,1,religion
হেরে এক বার জুতাদা বাইরাই সে । আবার দা দিয়ে কুবাইবো ছাগল রে ।,1,religion
সব গুলাই জাত শুয়ারের বাচ্চা ভন্ড,1,religion
ওকে যে দাওয়াত দিয়া নিয়া আসে তারা আরেক খানকির পোলা!!!!,1,religion
তাহিরি ভন্ড,1,religion
অবশ্যই ভন্ড তাহেরী আবাল,1,religion
কবর পূজারী মাজার পূজারী এই ভন্ড কুকুর গুলাকে জুতা দিয়ে পিটানো উচিত।,1,religion
✈✈✈✈🔫🔫🔫 মুরগি চোরের পাছায় ডুকবি আর মারবি।।।,1,religion
এই চার জন নাস্তিকের চেহেরা দেখা আমার মনে হয় পাপ হবে,1,religion
হুজুর হলো পুদাপোলা,1,religion
খানকির ছেলে গানজা খেয়ে হাবল তাবল বলে।,1,religion
মাদারির ফুয়া তুই খইলে কেনে আব্বাসি অপমান অইছে কানকির পুয়া,1,religion
নাস্তিকেরা সবসময় মিথ্যুক আর শয়তান এক নাম্বার। দুনিয়ার ময়লা আবর্জনা এরা সব নাস্তিক,1,religion
তর পুটকি দিয়া ডাং ঢুকানো দরকার,1,religion
লোপা একটা কুক্তা বাচ্চা,1,religion
লোপার মা পরপুরুষের দ্বারা লোপাকে জন্ম দিয়েছে বেশ্যা মাগি খানকি কুত্তার বাচ্চা,1,religion
শালারে নেমে মার যেন জিবনে আলেমদের সাথে গাদ্দারি নাকরে,1,religion
তুই সহ সব বাটপার সালারা,1,religion
এসব কি বাংলাদেশর পদান মনতি দেখেনা আমি এই নডির ফসি চাই,1,religion
সালা তুই কুত্তা,1,religion
নাস্তিকের মারে চুদি,1,religion
তুই বড় মাগির পুত,1,religion
হালারে পাইলে গোয়ায় বাশ দিতাম,1,religion
মহিলাটা খারাপ বেসি দালাল সাংবাদিক এই নাস্তিক কুওার বাচ্চাদের জুতা দিয়া বাইরাইয়া ভারত পাঠানোর দরকার,1,religion
এই নাস্তিক হলো ববুজাহেলরর বংশধর এই নাস্তিক হলফ বেজন্মা,1,religion
তুই হলি কউমি ইবলিশ সয়তানের বাচ্চা,1,religion
খানকির পোলা পুরো ওয়াজ দিয়া দেখা এই জায়গায় সবাই ভন্ড না,1,religion
হালার পুলা কাফেরের বাচ্চা,1,religion
হালাগো শুধু পিটানো উচিত ভন্ড পীর😡😡😡😡😡😡😡😡😡😡😡😡😡😡😡😡😡,1,religion
এ কুত্তা ওহাবী তোরে ফুটকি মারছে নি,1,religion
মিনিটে একটা খানকি মাগী ফোন দিছে উপস্থাপক মহিলারে দুচি,1,religion
ছাগলের নাম্বার বাচ্চার মতো লাফালাফি করতেছে,1,religion
বাই এইলুকটাকে আমি শপ্নে দেখছি কুত্তার বেশে আপনারাকি জানেন জানলে সবাইকে জানান,1,religion
একদম স্পষ্ট বোঝা যাইতেছে হালায় জুতার লাসার দিয়া নেশা কইরা বইয়া আছে হেতে চোঁখ টাইন্না মেলতে পারতেছেনা নিজেরে কেমনে এত কিছু দাবি করে? যারা এই ভিডিওতে ডিসলাইক দিসে সব কয়ডা দেয়ান মাগীর মুজুরের কামলা খাটা দিন মুজুর।,1,religion
টা কুত্তা টা কুত্তী কে বলছি ইনশাল্লাহ এই দেশে ইসলাম ছিল থাকবে তরা শত নাস্তিক এক সাথে হয়েও ইসলামের কিছু করতে পারবি না,1,religion
তুই হোলি জারজ সন্তান তোরে রাস্তায় রাস্তায় গিয়া গিয়া তোর আম্মা পর বেড়াইতে সাথে থাকে তোরে জন্ম দিছে তোর বাপ তো কমসে কম হাজারের কম হবে না জন্ম দিছে,1,religion
গিয়াস উদ্দিন চ্যাটের তাহেরি মালাউন ইতর মাদারচোদ ইতর কাফের বেশ্যা জাহান্নামী জারজ পথভ্রষ্ট গোমরাহ পথভ্রষ্ট গোমরাহ ইতর মালাউন ইতর মাদারচোদ,1,religion
মাগির বাসা কই আল্লাহর গজব পড়বে আল্লাহ বুঝার তৌফিক দিন,1,religion
চুদব চুদব নটি তকে তাহেরি কে নিয়ে কথা বলার যোগ্যতা তদের হয় কি ভাবে নষ্ট নারি হুজুরের বউয়ের ছবিটা মোবাইল চুরি করে তবে হুজুরের নামে আইডি অপেন করে আপলোট করা হয়েছে,1,religion
দুরু সালা মুরখের বাচচা। নবীজি তো হাজির নাজির ই তুই বুজিস কনো কিছু।,1,religion
তর বারী কই তুই আমার নামাম্ব নেয় তর নাম কি কুতার বাচ্চা,1,religion
তোরাতো নাস্তিক হুজুরকে কথাই বলতে দিচ্ছস না। কুকুরের বাচ্চারা।,1,religion
বাঞ্চুতের বাচ্চারা,1,religion
দেওয়ানবাগীকে যারা বিশ্বাস করে তারা কাফের অফ দেওয়ানবাগী কুত্তার বাচ্চা এতে কোন সন্দেহ নেই,1,religion
হালা একটা মাতাল হালা দেওয়ান বাঘি,1,religion
এই বেজন্মার গোয়ার ভিতর তেলযুক্ত অছেলা বাঁশ দিয়ে রাস্তার পাশে টাংগিয়ে রাখা দরকার।,1,religion
বাটপার কারা ছবি তুলা ইংরেজি শিখা হারাম বলছে আর কারা হালাল করছে বাটপার তুই জানিসই না বলদ কোথাকার,1,religion
নাস্তিক কে জুতা মারো।।,1,religion
হারামজাদা অওলিয়াগনের দুষমন।,1,religion
এই শালা নাকি পির ওর সেন্ডেল আর জুতা পিটা করা উচিৎ,1,religion
সালাই গাঁজা খাইছে,1,religion
ইসলামিক আলোচনার মধ্যে পতিতা নারী এবং নাস্তিক পুরুষ ওরা কি করে আমি বুঝতে পারছি না,1,religion
নাস্তিক দিয়ে দেশ বড়ে গেছে,1,religion
।এই মাদার চুদের পুলা হুজুর দের পিছনে লাগা বাদ দে।তোকে মরার পরে রোষট করা হবে ।ভন্ড চোর চুদদ পুরুষ ।মাগির পোলাও নিজের দোষ বের করেক।এই সুযের বাচ্চা চোখে দেখিস না ঐ সব লোকদের যারা দুনীর্তি করছে ।ওদের পর্দা ফাঁস করেক।ওদের বিরুদ্ধে কথা বললে তোর ধোনের রগ ছিরবে মাগি ।,1,religion
ভাই হালারা পাগল ছাগল ।,1,religion
আল্লাহর ধরা কঠিন ধরা।জেদিন ধরবে সেদিন বুঝবে নাস্তিক কুত্তার বাচ্চারা,1,religion
গাঞ্জা কি নাক ডুবাই খাইছিস?,1,religion
হালার পেট টা কিন্তু দেখার মতো,1,religion
এই কুকুর বাচ্চা কে যদি হাতের কাছে পাইতাম হাতলে কুকুর দিয়া রেপ করিয়া মাইরা ফালাইতাম,1,religion
এই বাগীকে জারজ সন্তানকে খ্যাঁংকির পোলাকে ফাঁস দিতে হবে,1,religion
হুজুর কওমি মাদ্রাসার শিক্ষক রা ছেলেদের পুটকি মারে এ বিষয় একটি ওয়াজ করিয়েন,1,religion
এ বাস করে কতগুল মূর্খ । যারা দেওয়ান বাগির অন্ধ ভক্ত সালা বাইঞ্ছদ নিজেকে দাবি করে ।নাউজবিল্লাহ । আল্লাহ্‌ আমাদের ক্ষমা করুন । আমাদের হেদায়েত দান করুন ।,1,religion
বেশ করে বছরের মেয়েকে বিয়ে ছেলের বউকে বিয়ে যাকে লাগাই তার মেয়েকে বিয়ে ওর বাবা মরে যাবার বছর পর জন্ম আর কি বলার আছে শুয়োরের বাচ্ছা,1,religion
সালা তো মুরগী চোর,1,religion
বোকাচোদা হাফিজুর ভন্ড শয়তান । বাংলাদেশের সবচেয়ে বড় ভন্ড ।,1,religion
এই ছাগলের বাচ্চারা সিদ্দিকি হুজুর কি বলছে মনদিয়ে শুন তার পর বিরুধিতা কর,1,religion
শালা এত বড় ভিডিও বানাস কেন মিনিট এ তো হালার বায়োগ্রাফি দেখাইলি 🤣🤣🤣,1,religion
দেওয়ান বাগীর পান্ডু পাঠাই পালাবো কুওার বাচ্ছা,1,religion
এডমিনকে মনে হচ্ছে পাগল চোদা মাথায় কিছু নাই,1,religion
আমি অই মাহফিলে থাকলে কুত্তার বাচ্ছাকে জুতা দিয়া পিডাইতে পিডাইতে অজ্ঞান করতাম।,1,religion
দেওয়ান মাগী রেলি মাদারচোদ,1,religion
সালা কোরআনের কি বুঝে,1,religion
এই সালা 😂🤣🤣🤣,1,religion
দেওয়ান বাগের মায়রে চুদি,1,religion
তরে 👡👡👡👡👡👡👡👡👡👡👡👡👡👡👡👡👡👡👡👡👡👡👡👡👡👡👡👡👡👡👡👡👡👡👡👡👡👡👡👡👡 দিমু কুতার বাচ্চা,1,religion
দিছে এগুলা কোন হালার পো 😈😈,1,religion
ভাইয়া এই কুত্তার বাচ্চা গোরে পিটানো ওচিত,1,religion
তুইত নিজেই বন্ড তাহিরির মত আলেম কে খারাপ বলিশ হালার পু হালা,1,religion
এই নাস্তিক দের মেরে ফেলা উচিত,1,religion
কুত্তার বাচ্চা রা মদ খেয়ে লেগেছে,1,religion
শালা তোর ভূরি দেখে বুঝা যায় তুই কেমন।,1,religion
শালায় একটা বাটপার বালের পোলা পিচ্ছি টায়,1,religion
রাম ছাগল কি কই আচুদা তাহেরি,1,religion
কুকুরদের মাঝে আপনার কোন মুল্য নাই।।এরা নাস্তিক কুততার বাচ্ছা,1,religion
দেওয়ানবাগীর ভন্ড পীরের গালে গালে জুতা মারি ওই পণ্য রে পণ্য তার তো জন্ম ঠিক নেই সে তো নাস্তিক শালার ভন্ড তাহেরী জুতা মার শালারে গালে ইউর বাস্টার,1,religion
দেওয়ানবাগীর ধনের চিপায় গরম গাজা ভরে দাও,1,religion
সালারা টাকার চুদা দেশ ভালো হইবো কোথাথেকা টাকার কাছে সব বিকরি কইরা দিছে ইমান আমল খোদারেও,1,religion
আমার বড় ইচ্ছে তাহেরী কে গুয়া মারবো। ওর পাছার সাইজ ভাল।,1,religion
খানকির ফুলা হাফিজুর রহমান ভন্দ আর তুই জারজ,1,religion
এবার তোর মারে না তোর চুদার দরকার খাননি মাঘি,1,religion
এই নাসতিক গুলাতো পসুর কাতারে ও পরেনা এগুলা মানুস রুপে এই দুনিয়ায় কেনো আছে কুততার বাচচারা,1,religion
এদের কে কুত্তা লীগ লায় দিয়ে মাথায় তুলছে,1,religion
মুরগী নাস্তিক এর লক্ষ খোজে দালাল সব,1,religion
নবীর চুল কাধ প্রর্যন্ত ছিলো কোন হাদিসে আছে রেফারেন্স দাও সালা ভন্ডের বাচ্চা!!,1,religion
এই কুততার বাচচাকে জদি পাইতাত তাহলে ও বউ বিতরে বরে দিতাম চোদানি মাগির পোলা নাসতিকের বাচচা সাহস থাকলে সামনে আয় তোরে তোরে জবা করমু,1,religion
তর থেকেউ ভালো তাহেরি হালা ভালপাকনা,1,religion
আমি দেওয়ান বাগীর ছেলের কথা টা বিষসাস করছি তবে অন্য কোনো রেংক না। দেওয়ান বাগীর পেটের রেংক দিছে এই কুত্তার বাচ্চার মত আর কেউ রে পেট দেয় নাই।,1,religion
তুই একটা মাদার এর বাচ্ছা মিথ্যা কথা বলিস কেন,1,religion
শালা বাবা ছাড়ে নাই,1,religion
এদের বিশাল বড় ভোট ব্যাংক আছে।তাই কোন পলিটিকাল পার্টি আর প্রশাসন এদের ঘাটায় না।আর এই সুযোগেই এরা আমাদের অবোধ মানুষদের বোকাচোদা বানাইতেসে!,1,religion
মাগি তুমি তোমার নিজের চিন্তা কর অন্যের গিবত বলা ঘুনার কাজ মাদার চুদ তুই একটা জারজ সন্তান মাগি,1,religion
জুতা মার সালি আর দুই সালারে,1,religion
নাস্তিক কুত্তার বাচ্চা গুলোকে কি যে করতে মন চাইতেছে। নাস্তিক গুলার ইসলামিক জ্ঞানের মারাত্বক স্বল্পতা রয়েছে।,1,religion
শালা কথার ভুল ব্যাখ্যা করিস কেন?লা মাযহাবীর বাচ্ছারা!,1,religion
সালারা কি বলে নিজেও বুজে না গাজা খুর সালা,1,religion
এই খানকির পুলারা তোদেরকে সামনে পেলে জোবো করবো,1,religion
দেওয়ানবাগির বউরে মেয়ে খারা করে পুন্দানের কাম সালার মায়রে,1,religion
তোমার খোগা দা বাশ ডুকাইব মাগি,1,religion
তোর জন্মের দুশ ছেনেলকারি নাস্তিক জন্মের নাই আস্তিক,1,religion
ওই সালা ভন্ডামি পীর দের মুখোস খুলে দিয়েছেন আললাহ আপনাকে ভালো করুক আললাহ ছারা কারো কাছে মাথা নত করা যাবেনা,1,religion
কাফেরের বাচ্চা কাফের।,1,religion
সিদ্দিকি হুজুরকে ভন্ড বলার সাহস তোকে কে দিছে সালা কুলাংগার,1,religion
শুয়োরের বাচ্চাদের জব কর,1,religion
চারটাকেই জুতা মারা উচিৎ। নাস্তিক কোথাকার!,1,religion
ছুতমারি খানকি নাস্তিকরা বোঝার আগে আগে কথা বলে। জানেনা ঠিকমতন কালিমা আর এ্যাডবান্স কথা বালার জন্য আগাইল।মামুনুল হক আপনি এই বেহায়া বে পর্দা উপস্তাপিকা মেয়ের সামনে অনুষ্টানে নাজাওয়াটা আপনার জন্য উত্তম ছিল।,1,religion
মাদার চুদের বংসদর,1,religion
এই চার কুত্তারে কে কে পাগলা কুত্তার মত পিটাইতে চাও,1,religion
খানকির পোলা তাহেরী,1,religion
বলদ বোকা ভন্ড হুজুর,1,religion
তরা সাউয়া মুকা নামাজের সাথে পূজার মিল করস সালা,1,religion
দেওয়ানবাগীর বলদ ভক্ত সবগুলা গাজা খায় মেয়াদউত্তীর্ন,1,religion
শালার নাস্তিকরা যা শুরু করল এরাতো আমাগো রুটি রুজির রাস্তাই বন্ধ করে দিচ্ছে। এখনতো আর আগের মত মানুষ আমাগো দাওয়াত খাওয়া দাওয়া খাতির আপ্পায়ন করতেছে না। শালার নাস্তিকরা তোরা কি আমাগো খাওয়াবি? আমাগো বউপোলাইনগো খাওয়াবি? আমাগো পেটে এইভাবে লাত্তি কেন দিতেছিস। ঈমামতি কইরা কোনমতে খাইয়া পইরা বাইচ্চা আছি। মাইনষের বাড়িতে কত্ত মজার মজার ফ্রি খাওন কি তোরা খাওয়াবি? আমরাতো এই ধর্মটা না থাকলে কি কইরা খাইতাম।,1,religion
এই চার কুত্তার বাচ্চারে জবা কইরা দে,1,religion
যারা ডিসলাইক দিছে তাদের বগা কাইটা দেশি মুলা ঢুকিয়ে দেওয়া উচিৎ।,1,religion
মিজানুর রহমান আজহারি মত জাহেল কে জুতা মরা দরকার রাসুল সা কে নিরক্ষর বলেছেন আবু জাহেলের আপন ভাই শয়তান মিজানুর রহমান আল্লাহ ও রাসুলের শানে যারা বিয়াদবি করেছে আল্লাহ তাদের কে হেদায়ত করুন আমিন,1,religion
ওরে আহালে সয়তান আফগানিস্তানে জন কুরআনের হাফেজ মারা গেলো আমেরিকার হামলায় তোদের কোনো প্রতিবাদ নাই চরমোনাইর পীরের নামে মিথ্যাচার করোছ তোদের কপালে জুতা মারি ইবলিশের বাচ্চারা,1,religion
কুত্তার বাচ্ছা,1,religion
এই খানকি মাগির পোলা তোর বাপের আর তোর কপালে জুতার বারি চুত মারানির পোলা ভালো হয়েজা না হলে জিহাদি জনতা তোদের কুকুরের মত পিটিয়ে মারবে।তোর বাপ ছিল ভন্ড মুনাফিক। তুই ও ভন্ডামি শুরু করেছিস।,1,religion
আস্তাগপিরুল্লাহ নাউজুবিল্লাহ কি বল্ল এই নাস্তিক এর বাচ্চা,1,religion
দিয়ে নিজেকে ভণ্ডদের ভক্ত প্রমাণ করার কি দরকার? শালারা ইসলামকে দংশো করে দিচ্ছে।,1,religion
শালার লজ্জা নেই মুরগী চোর,1,religion
সব শালারা ভন্ড। ভন্ড জিকির,1,religion
সালারে বান দে,1,religion
এই সমস্ত ভন্ডদের পাছার ভিতরে বাঁশ দিয়া দ্বারা কইরা রাখা উচিত রাখা উচিত,1,religion
ভাই তুইতো বিশ্ব মাদরছোদ শালার বেটা তোরে বক্তা নানাইছে কে,1,religion
তার পাচায় অর্ধ গরম রড বাহিরে ঠান্ডা অংশ রেখে ডুকানো উচিত 🙂 যাতে তার মুরিদ রা না টেনে বের করতে পারে 😁 মাগির পোলা তর মাইরে চুদি রোজা রেখে এসব সহ্য করার ছেয়ে তরে গালি দেওয়া বেটার ☺,1,religion
মাগির জি মাগি,1,religion
তুই চুর তর বাবা চুর। হালারপু হালা। মূর্খের গুষ্টি। বালা কতা কানেদা যাইবো তোর। বালের চেনেল খুইলা বসে রইছত। বিষ খাইয়া মর তুই।,1,religion
সোনার জিকির তোর মাদার চোদ,1,religion
বালপাকনায় ফেসবুক ও ইউজ করে 🤣 শালা! তুই তাহেরি নিয়া উল্টাপাল্টা কথা কস এইডা বেয়াদবি না?,1,religion
দুর হয়ে যা মাদার,1,religion
সালা একটা ভন্ড,1,religion
এই ফাতরাগুলোরে পুলিশে ধরায় দেয়া দরকার। আবালের গুষ্ঠি সব!,1,religion
গাদা তুই তোর বাপ নোমান কাসেমীরে চিনসনা ওলিপুরিরে চিনিস । পাগল ছাগলের দল,1,religion
কুত্তার বাচ্ছা দেখ মানুষ কেমন কমেন্ট করছে শালার জারজ সন্তান ও নাস্তিকের দল,1,religion
মাগির ফুলা,1,religion
শালা হারামজাদা কি জুতা মারো সবাই শিশু বক্তা তোর মাকে চূদি আমি এবং কুত্তা দিয়া চোদামু,1,religion
বাইনবচোদ তোর পাচায় বাশ। হাফিজুর রহমানের পায়ের ধুলির যে মর্যাদা সেটাও তোর নাই।,1,religion
এ শুয়োররের বাচ্চা মাদারচোদ হারামি তোকেজ্দি আমি সামনে পাতাম তাহলে তোর হাত কেটে ফেলে দিতাম আর তোর মুকে এক কুতিজুতে মারলাম মাদারচোদ হারামি কুকুর শুয়োর জানোয়ার 👠👡👢👟👞👞👟👠👡👢👞👟👠👡👢👞👟👠 👡👢👞👟👠👡👢👞👟👠👡👢খাজুতা মাদার চোদ,1,religion
লুপা তোরে চুদ্দা তোর বানার ফাটামি খানকি মাগি,1,religion
চারটাই পাগল চোদা হুজুর বাদে,1,religion
তারাই হক্কানি আলেম আর দেওয়ান বাগি হয়ছে ইবলিস শয়তানের বড়টা শালা বান্নদির বাচ্চা,1,religion
খানকির পোলা তরমাইরে চুদি ওদেরকে বন্ড বলিস কেন,1,religion
মুরগি চোর সাহরিয়া কোন চেটের বাল এখানে সব গুলা নাস্তিক একটা লোক ছারা,1,religion
মামুনুল হক আপনাকে সালার নাস্তিকের বাচ্চারা।,1,religion
কুকুরের বাচ্চা এই‍্ রকম করে দিলি কেন,1,religion
শালা তাহেরি ভন্ড,1,religion
ভন্ড বক্তা খানকির পোলা,1,religion
এরা হলো পতিতালয় জন্ম হয়েছে,1,religion
হালার পুত তুই একটা ভন্ড ভন্ড ভন্ড ভন্ড তুই একটা ভন্ড,1,religion
হজ্জ কে অসম্মান করচে জারজ,1,religion
মারেন মারেন তাহেরি ভন্ডর পুটকি মারেন আই হায়,1,religion
তুই একটা শুকুরের বাচ্চা তুই কি বুঝবি?একটাকার লেখা পড়া করিস নি দশটাকার নিয়ে লাফালাফি করিস।,1,religion
ফেরাউন এর বংশধর সালা,1,religion
আল্লাহ তোদের হেদায়েত করুন তবে আমি তুদের জুতাদিয়া পিটাইতে পিটাতে জিগ্গাশ করতাম তুদের সৃষ্টি করতা কে বল মাটির মুর্তী যে মর্তী মানুষ বানাছে তুরাতু ইবলিশ শয়তান আর এই মুসওলা তুর মুস ওক্তাওপরেদিকে টাইননা চিরতাম তাহলে তুর ভিতরে একটু চেতন আসবে জাহান্নাম কি জিনিশ আর লোপা তুর এতো সেক্স তুর লজ্জাস্তান দিয়া আগুন ওয়ালা ওততাপ্ত রট ডুকানো উচিত তবে সঠিক মজা পইবিএচারা তুর হবেনা,1,religion
আমার মনে হয় তাহেরী তুকে প্রথম চুদেছে,1,religion
তর জতা মারি কুততা দেওয়ানবাগি,1,religion
ভাই দেয়ানবাগী তো নাম্বার ভন্ড এইবার নাম্বার ভন্ড চোরমুনাইকে রোস্ট করেন। প্রমান লাগলে দিবো যে হালায় ভন্ড।,1,religion
বুজাজার চাচাই মলম বেছরা,1,religion
তরে পায়লে গুয়া দিয়া বাশ দিতাম বন্ড শালা দেওয়ান বাগি,1,religion
মাদারচান খাজাবা,1,religion
মাগিটাকে আমার দরকার ওর এত পাওয়ার ওরে আমার চোদার দরকার আমি জদি না পারি ওর সাতে ওর ভোদায় গুলি দিয়া পাওয়ার কমামু।,1,religion
এই ভন্ড মাদারচোদ নিচে দেখ তরে পুটকি মারতেছে জনগনে তর লজ্জা থাকলে কোন দিন মাইকের সামনে বসবেনা ওকে,1,religion
দেয়ানবাগি কে কুত্তা দিয়ে খাওয়ানো উচিৎ।,1,religion
জানোয়ারের বাচ্চারা,1,religion
কুত্তার বাচ্চা তুই এতো বড় দাড়ি রাখলি কেন এইসব কাফের দের মানুষ জুতা দিয়ে পিটিয়ে মেরে ফেলুন,1,religion
শালা ভন্ড আল্লাহকে নিয়ে গীত গাওয়া হচ্ছে নবীকে নিয়ে ডান্স করা হচ্ছে এরকম ভন্ডামি কোত্থেকে আসে পীর ছাড়া কেউ এরকম করতে পারে না,1,religion
সালার বেটা সালারা মানুষের জাত না,1,religion
ভন্ড কুকুৰেৰা শালা পাচ জন,1,religion
🐐 ছাগল এর তিন নাম্বার বাচ্ছার মতো বেবে করে কেনরে এমডি,1,religion
আমি আমির হামজা কে চুদি মু,1,religion
মুরগি কবির অবসসই নাসতিক,1,religion
খাটাশের বাচ্চা খাটাশ!,1,religion
শালা কুকুরের বাচ্চা তুই জারদ সন্তান হারামি কারন গালি দিলে কবিরা গোনাহ তরে পাইলে জুতা পিটা করিব শালা মাজার পুজারী সুন্নী শয়তানের দল আর রেজবী মানি কাফেরের দল,1,religion
তুই কি মাগী জান তোর বাব কে।,1,religion
সালার পুত তুই আরো বড বন্ড,1,religion
ভন্ডের বাচ্ছা ভন্ড,1,religion
এই কুকুর এর বাচ্চা তুলার বস্তাকে খুন করে যদি ফাসির মঞ্চেও উঠতে ও পারতাম নিজের জীবনকে ধন্য মনে করতাম 😑😑😑,1,religion
সালা লুচ্ছা,1,religion
পাকনামি করো পাকনার বাচ্ছা কোন বাটপারা এসব কুলাংগার দের শ্ষেজে ওঠায়,1,religion
মাশাল্লাহ তাহেরির মারে চুইদ্দা বসেন,1,religion
কুলাংগার জারক ভন্ড শয়তান মাজার পুজারি তাহেরি কে জুতা মারি।,1,religion
শালা বেয়াদব শাহরিয়ার গালে জুতা মারা উচিত,1,religion
কুওার বাচ্চা সাথের গুলোও কুওার বাচ্চা।,1,religion
আমির হামজা মাদারি,1,religion
এই নডির পূলা ইউটূব অলা তূই উলিপূরিরে ভনড ভলছছ কেশালা কলদে,1,religion
মাদারচোদ লোপা তরে পাইলে আমি কেলাইতম আর খেলাইতাম। তকে দেখে চুদার ইচ্ছা করে,1,religion
শালা পগল কোরানের কোন কথা নাই,1,religion
দেওয়া বাগি শালা কাফের। শালা একটা ভনড়ো ভনড়ো।।।।,1,religion
দেখা যাক কতগুলা দেওয়ানমাগী ফ্যান ডিসলাইক চোদায়!,1,religion
জুতা মারার জন্য কে কে আছেন লাইক হবে,1,religion
মার ওহাবির বাচ্চারে মার জোতা দিয়ে মার এই শালারাই জংগি,1,religion
টাকার কামলা শালায় মিজানুর হুজুর কে নিয়া ভিডিও করিছ? কুওার বাচ্চা,1,religion
মাজার পূজারীরা ডিসলাইক দিছে 😡😡 সালারা,1,religion
তুমি কানকির পোলা তুই ওয়াজ মাহফিলেও কি করস। শিশু বক্তব্য কমনে হয়।,1,religion
সয়তানের বড় কাকা সালার পুতে,1,religion
সব আবাল চোদা শ্রোতা,1,religion
সালা তোই এতো বড় জানোয়ার ?? সালা তোর যে মরন কেমনে হবে??,1,religion
ভন্ড শালারা এদের কে মেরে ফেলা উচিত।,1,religion
বসেন বসেন বইসা যান তাহেরি তোর মার গুদ মার,1,religion
আমি যদি ঐ জায়গায় থাকতাম ঐ মালাওনের বাচ্চাদের পাছায় এমন ফু দিতাম সাড়া জীবন আগুন জ্বলতো,1,religion
গাদার বাচ্ছা গাদা তুই হইলি সব চেয়ে বড় শয়তান।।।।ছাগল একটা,1,religion
মাদারের বাচ্চা তোরে পাইলে জুতাপিটা করুম।তোরা তো কেয়ামতের আলামত তোদের কারনেই আজ দেশের এই অবস্থা।,1,religion
মুরগি মাগি ছায়া দালাল,1,religion
খানকি মাগির বাচ্ছারা তগো গরম তেলে ফেলা উচিত,1,religion
রে কুত্তা দিয়ে পুটকিমারা তাহলে ফেয়ার শুরু,1,religion
এই৷ ৷ মাদারচুদের৷৷ জন৷ মানুষ,1,religion
এরকম টকশোর মারে চূদি খানকির পোলারা যেত নাস্তিক আছে এই টকশোর ভিতরে দেখতাম শুধু একজন ছাড়া,1,religion
শালার পোলা তর শোনার গোরে বাল ঝালাইছে,1,religion
সালার বেটাকে জুতার বাড়ি মার,1,religion
মুরগী চোরের বাচ্চা কে জুতার মারা হোক,1,religion
হুজুর আপনে এসব জানোয়ারদের সাথে এক টেবিলে বসা উছিত হয়নি,1,religion
গুন সওয়াব শালা পাগলচোদা,1,religion
খানকিরপুলা তুই আগে ঠিক কর🤬🤬🤬,1,religion
রাত একটার সময় ওয়াজ করে গণ মানুষের ঘুম নষ্ট করে কিসের হেদায়তের কথা বলিছ? তোর এই ওয়াজের কারণে ঘুম যেতে না পেরে যদি কারো ফজরের সালাত মিস হয়ে যায় তাহলে তোর কয়েক হাজার ওয়াজ দিয়ে ও কি ওই সালাতের ক্ষতিপূরণ দিতে পারবি? শালা মাঝার পূজারী ভন্ড।,1,religion
নাস্তিকের বাচ্চারা কুকুরের চেয়েও খারাপ,1,religion
তরে পুক্কি মারব ভাল করে মাদার চোদ,1,religion
আস্তাগফিরুল্লাহ। কিরে তুই ঠিকই তো ভন্ড। পাগলি মাথায় দিয়ে নামাজ পড়লে এক রাকাতে সত্তর রাকাতের সওয়াব পাওয়া যায় এটা জাল হাদিস। আর তোর এ ব্যাপারে কোন ধারণা নেই। এই লোক তো ঠিকই বলেছে। আসলেই তুই ভন্ড।,1,religion
দেয়ান বাগি কুত্তার বাছ্ছা,1,religion
কুকুর এর বাচচারে মারো মাগির ফুরি। চুতমারানির পুরি।,1,religion
যারা এই রোস্টিং ভিডিওতে আনলাইক বাটন ক্লিক করেছে তারা নিশ্চয় দেওয়ান বাগীর মুরিদ। আমার কথা হলো সারা বছর বুজুর্গদের থেকে জেনে এসেছ ইসলামের কথা আর কোথাকার কোন দেওয়ান বাগী এসে নতুন হাদিস বানাচ্ছে সেইগুলাকে মানুষ কেমনে বিশ্বাস করে।এইগুলা এক নাম্বারের ভন্ড পীর।যতসব আবাল মুরিদ।প্রত্যেকটারে ধরে থাব্ব্রাইতে মন চাইতাছে।সবগুলারে মারি দেওয়ান বাগীর নাম ভুলাই দেওয়া দরকার।রাগ উঠতেছে বেয়াদবের উপর,1,religion
একটা ইমাম এর সামনে এই মহিলা মাথায় ঘুমটা দেয়নি এর থিকেই বুঝাযায় এই মহিলার চরিত্র ভেজাল এই মহিলা একটা জারজ সন্তান,1,religion
সব গুলো জারজ,1,religion
কুত্তার বাচ্ছারা,1,religion
যাদের জন্ম ও রক্তের সমস্যা । তারাই জারজ সন্তান । আর তারাই হল নাস্তিক । এরা কপাল পোড়া দুর্ভাগা জাতি।সমাজের কিট।,1,religion
ধূর মাগি,1,religion
শাইখ মামুনুল হক সাহেব কে আন্তরিক ধন্যবাদ এতো ধৈর্য্য নিয়ে শয়তানদের সাথে কোরআন সুন্নাহ আলোকে কথা বলার জন্য। আমি থাকলে হয়তো শালাগো জুতা পিটা করতাম🙄🙄🙄,1,religion
ওই শালা তর নাম আর ঠিকানা দে আহমাদ শফি রেজাউল করিম আর ওলিপুরি ভন্ড কে বলসে তরে,1,religion
শালা তুই ভন্ড পীর কুকুর তুই,1,religion
জীবন মাএ শুরু এখন ই গিবত গাওয়া শুরু সালা বেয়াদব,1,religion
এই সালাই গাঁজা খাইছে,1,religion
বালপাক না তুই কি বুজচ,1,religion
কবিরা মাগীর হোলা হেড়া হুড়া হাড়াইলামু মাদারচোদ।,1,religion
কিরে তুই কি তাসনিনেসন খানকির পোলার মতো কথা কস কেন তোরে চুদা হবে তুই হালা ডাইলে চাইলে খিসুরি করে পেলসস সব,1,religion
শালাদের গুলি করে মারা উচিত,1,religion
শালা তাহিরি তোর মার ভাতার কটা,1,religion
বেয়াদপ নামবার ওয়ান তুই দুই দিনের ছেলে ভালো মন্দের কি বোজস,1,religion
মাগির হোত তোইমা পাতেমার জুতার জুগ গতা হচনা,1,religion
সালার পোলা তরে যদি এখন আমি কাছে পেতাম তরে লেংটা করে পেটাতাম। মাদার চোর ওয়াজ করতে আচ্ছিস নাকি বেপসা করতে আচ্ছিস খানকির পুত,1,religion
জুতা মার সালাগরে।,1,religion
তরা হলে জারুজ সন্তান তদের জম্মের ঠিক নাই মাদার চোদ।,1,religion
ত্রই কূততার বাচছা তরিকা বলদা হালায় বলে,1,religion
নাস্তিকের জন্মের ঠিক নাই। এই জনের রক্তে ভ্যাজাল আছে।,1,religion
এই সালার পুত তোর নাম্বার দে।সালার পুত ভন্ড পির নামে কলঙ্ক মাদারীর ছোদ,1,religion
ভাই এই মাগি কোথায় থাকে,1,religion
যারা হুজুরদের সমালোচনা করে তারা তাদের মা বাবার জারজ সন্তান,1,religion
এই কুত্তার বাচ্চারা তোরা কি ইহুদি ধর্ম নাকি কয় বার বলছি মদিনার নাম না নেওয়ার জন্য,1,religion
বেয়াদবের বাচ্চা তাহেরি মানলাম খারাপ তর বড় নাকি ছুট বেয়াদবের বাচ্চ 😠😠😠😠🤬🤬,1,religion
খানকির পোলারে পাইলে জুতা দিয়া পিডাইতাম,1,religion
শালা মুর্খ ভন্ডর মাইক কেরে নেয়া হোক কি ভাবে ওয়াজ করতে হবে তাও জানেনা ওকে জুতা পিটা করে একান থেকে গার দাক্কা দিয়ে বের করা হোক সাহজালালের সাথে ব্যয়াদবী করে মুর্খ সাহজালালের পায়ের জুতার দাম ও হবে না।,1,religion
বসেন বসেন শালারে বাশ দেন,1,religion
শালারাই শুধু একটা আরেকটার গোয়ার পিছনে বুজলাম না জাহান্নামে যাবা আলেমরা আগে সাধারণ মানুষ তো গোমরা হয়ে যাবে,1,religion
তিন টা খানকির মাগির পুয়া,1,religion
তোরে জদি কোন দিন হাতের কাছে পাই সেইদিন তোর কপালে বহুত দূঃখ আছে মাদারচোদের বাচ্চা ভন্ড,1,religion
চার কুত্তার বাচ্চার মুখে কুত্তা দিয়া পেশাব করাতে হবে,1,religion
নাস্তিকদের জুতা দিয়ে মারা উচিৎ,1,religion
বান্দিনির জি তরে মনে করছিলাম ভালো তুই দেখতেছি মাগি নাম্বার ওয়ান তরেও কি লাগাইছে নাকি,1,religion
এই চ্যানেলট একটা দুই পা ওয়ারা ছাগলের।,1,religion
আরে আবালের দল,1,religion
আমি যদি কখোন ও দেওয়ানবাগি কে নিজের চোখের সামনে দেখতে পাই তাহলে ও জায়গাতেই আমি ওই জানোয়ারের মুখে গোবর ছুড়ে দেব। ওই জানোয়ার কুত্তা কে খুন করলেও আমার রাগ ঠান্ডা হবে না।,1,religion
কুত্তার বাইচচা নাস্তিক,1,religion
গিয়াসউদ্দিন তহেরি শুয়োরের চুদা,1,religion
শাহারিয়ারের হাত পা বেধে কুকুরের খাদ্য বানানো উচিৎ। খানকির পোলা নাস্তিক।,1,religion
সালা মাদারচুদ ইউটুবার,1,religion
মাদারচোদ তুই কাকে কি বল! আগে পুরো কাহিনী শোন! তারপর বল! বাংলাদেশ একটি মুসলিম দেশ! ইসলাম নিয়ে ঠাট্টা করার জায়গা পাওনা! তাড়াতাড়ি পোস্ট ডিলিট কর,1,religion
সানি লিওন গান চালা মাদার চুদ ভন্ড,1,religion
বুঝলাম না এর মত কাফেরের বাচ্চা এখনো বাংলার জমিনে আছে কেমনে!!!!? কয়েকদিন আগে এক ভন্ডকে গ্রেপতার করা হয়ছে যে বলছিল আমার নবী মুসলমান না!আর এই খানকির পোলা তো খোদ বলছে মা ফতেমা তার স্ত্রী নাউজুবিল্লা একে কেন প্রশাসন কিছু করতে পারছে না!??না কি প্রশাসনের কোন দুর্বলতা আছে!???,1,religion
যারা দেওয়ানবাগীর বিরুদ্ধে কমেন্ট করছ তোরা সব জারজ সন্তান কুত্তার বাচ্চা।,1,religion
এই সব শালার পুতরে জুতা মারার দরকার।,1,religion
ভাই কিছু মনে কইরেন না জীবনে যা বলিনি আজ তাই বলবো ।। আশা করি পাপ হবেনা।।। দেওয়ানবাগী খানকির পোলা তো সেই লেভেলের। সকল মুসলিমের উচিত ভন্ড দেওয়ানবাগী খানকির পোলাকে মেরে ফেলা।। আমার বিশ্বাস ওকে মারতে পারলে বিনা হিসাবে জান্নাত পাওয়া যাবে,1,religion
এই শালা একনামবার ভনঠ,1,religion
এই সমস্ত কুকুরদের জন্য ইসলাম আস্তে আস্তে ধ্বংস হতে যাচ্ছে,1,religion
ভণ্ড তাহেরি কুত্তার বাচ্চাকে ধরে মাথা কামিয়ে কালা কুত্তার পায়খানা মেখে দাও । ল্যাংটা করে পাছায় আলকাতরা মেখে দাও ।,1,religion
এই জানোয়ারকে মেরে গেছে না কেনো,1,religion
এখানে মামুনুল হক বাদে ওই মাগি সহ সব নাসতিক।,1,religion
একটা জারজ সন্তান মনে হয়,1,religion
মিজান হইলো একটা শালার পুত,1,religion
আমিৰ হামজা হুজুৰ আপনে ওই শালা তাহেৰী কে জুতা মাৰেন নালি আমি শামনে পাইলে শালাকে জুতা মাৰতাম ও শালা তাহেৰী এক মাদাৰচোত শালা,1,religion
ওকে ধরে এনে ফাঁশি দেওয়া হোক। হারামির বাচ্চা।,1,religion
দেওয়ান মাগী 🤪,1,religion
ঐ হারামী মাজারে মাজারে গাজা খায়। এবং মাগী বাজী করে গাজার ব্যাবসা করে। একারণে ওর আতে ঘা লেগে ছে।,1,religion
এইটা একটা কুত্তার বাচ্চা,1,religion
তোরা সত্য খবর শুনাতে না পারলে বুঝবো যে তোদের মা সুকরের সাথেই সঙ্গম করায় তরা ঐরকম মিথ্যেবাদী হয়েছো,1,religion
এই কুত্তার বাচ্চাকে মারা ফরজ হয়ে গেছে সালা জালেম।কুত্তায় জন্ম দিছে বেয়াদবরে।,1,religion
চোদানির জাত,1,religion
খবিসের বাচচা,1,religion
খানকি মাগিরে কুত্তা দিয়ে চুূদামু,1,religion
সঠিক কতা হক কতা বললে সালাদের সরিরে গায়ে আগুন জলে? লাল পানজাবি ওলা সালারা গানজা খুর?,1,religion
তোর বোন মারে লয় ভিডিও কর বায়ানচোদের বাচ্চা,1,religion
সালা ইউটিউব চ্যানেল কুকুর বাচ্চা মিথ্যা কথা কেন বললে সালা,1,religion
জুতাদিয়া মার শালারে,1,religion
তাহেরি মাগির পুলারে আমি পাইলে পরিস্কারভাবে দুয়ে পেলবো,1,religion
তোর মোরগ চোরের মাইরে চুদি,1,religion
মুৱগি চুদা আৱ মাগিকে চুদা দৱকাৱ,1,religion
শুয়েরের বাচ্ছা খবিশ বন্ড নাম্বার দেও কেউ ওর শালাকে সিলেট আনিয়া এমন বাদাম দিবো ওয়াজ করা শিখাইয়া দিবো,1,religion
ভন্ড কুত্তার বাচ্চাকে জুতা পিটা করে তার পরে ফাসি দাও,1,religion
মাদারছোদ মিজানুর রহমান আজহারী রে নিয়া উল্টা পাল্টা কথা বললে তুর জিহ্বা ছিরে পেলমু,1,religion
কত্তার বাচ্ছারা ভন্ডদের মারে চুদি,1,religion
এগুলারে পাগলা গারদে ফাঠানো হক ভনডো হালারা,1,religion
জুতার মালা গলায় পরিয়ে রাখতে হবে শালার পোলারে,1,religion
এই চার জনের মুখে জুতা মার। আর এক মাগি ফোন করে মারা খাইতে চলে গেছে,1,religion
খানকির পলাগো কুততায় পন্দায়া জরমো দিছে,1,religion
দেওয়ানবাগিকে জিবিত অবস্তায় চিতায় তুলে পুড়ালেও আমার গার ঝাল মিটবে না ওর শাস্তি তাতেও হবে না আমার মনে হয় যে মাটিতে ওই সালার কুত্তার বাচ্চার দাভন করা হবে ঘৃনা করে ওর দিকে তাকিয়ে দেখবে না কি বলেন ভাইয়েরা?? প্লিজ একটা লাইক আর আপনার মূল্যবান কমেন্ট দ্বারা আপনার মতামত পেশ করুন।,1,religion
এখন ঘুম থেকে উঠলাম তাই গালি দেওয়ার কোন মুড নেই না হলে তাহেরি নাফরমান কে গালি দিতাম এক জানোয়ারের বাচ্চা দুই কুত্তার বাচ্চা তিন বাইঞ্চোদ মাদারচোদ খানকির পোলা,1,religion
এসব কুকুরের বাচ্চা দের জুতার মালা পডিয়ে দেও,1,religion
ম যাহানাম পাবে দেওয়ানমাগী আবাল,1,religion
কত আর চুদা লইবি নারী নামের কলংক তুই,1,religion
দেওয়ানবাগী একটা শুয়র এর ছেয়ে খারাফ,1,religion
এখানে দেখলাম কয়েক টা রামছাগলের বাচ্চারা মাগীর বাচ্চারা সয়তানের কনডম ছিড়া ধনেরা কোন বাল না বুঝে ই হুজুর কে ভিবিন্ন ভাবে গালা গালি করেছে এদের কে ভলতে চাই তোরা ই গাট্টির চোদা শালারা সব ওহাবী নাস্তিক হারামজাদার দল।,1,religion
সালার মুখে জুতা মার।তুই রেডি থাক তোর কপালে ভোগ আছে।,1,religion
শুয়ারের বাচ্চারা।,1,religion
আমি যদি সত্য কোন রাষ্ট পক্ষের আইন জিবি হতাম তাহলে এই সব নাস্তিক দের জুতা মেরে বাংলার জমিনে ফাসির আদেশ দিয়ার সিদ্দান্ত নিতাম এবং ফাসি কার্যকর করতাম কুত্তার বাচ্চার মুরগী চুরার জুতা মার বিয়াদব,1,religion
তোর মত বেয়াদব আর নেই,1,religion
নাস্তিক গুলা মুরখ৷,1,religion
এই সকল দেওয়ানবাগী মাদারের বাচ্চা এখনও আইনের আওতায় আসলো না কেন ??,1,religion
চোদনার পো দেওয়ান বাগি। পিটাতে হয়,1,religion
না বলে পারলাম না তোর মত টা বাইন্চোদ দেশে জন্ম হয়েছে বলে আজ এ দশা ফাজিল মাদ্রাসায় পড়লে পাজিল হয় এটা কি তোর পতিতা মা বলেছে ?? দোষ দেওয়ান বাগির তাকে দোষ দে ফাজিল মাদ্রাসাকে নয় বাইন্চোদ,1,religion
তাহেরি হল একটা বন্ড আর আমির হামজা হলো একটা মিত্তুক শালা আমির হামজা মিত্তা বাদী,1,religion
শালা কে জুতা মার ভন্ড শালা,1,religion
বাল পাকনার বাচ্চা গীবত করে।,1,religion
জুতা বারি সালা পুত দেওয়ানবাগি,1,religion
হে আল্লাহ তুমি এই নাস্তিক কুত্তাদের ধ্বংস কর,1,religion
এই ফতোয়া চোর চরভোদাই ভন্ড পীর ইসলামী লেবাসধারি ডিজিটাল মুনাফিকের দালাল। একে জুতা দিয়ে পিটিয়ে বঙ্গোপসাগরে ডুবে ই মারা উচিত। এই ফতোয়া চোর চরভোদাই ভন্ড পীর ইসলামী লেবাসধারি ডিজিটাল মুনাফিক থেকে সাবধান হোন বাংলাদেশ মুসলমান।,1,religion
কুত্তার বাচ্চা মিডিয়া তুই পুরোটা বয়ান না দিয়ে ভন্ড কেন বলছিস তুই কি সুনস নাই যে উনি পুরোটা বয়ানে কি বলেচে তোর জন্মের ঠিক আছে হাফিজুর রহমান তো ঠিক কথাই বলেছে উনার জুতা টানার জন্য তোকে নিবে,1,religion
এই মাগি কি বালের উপস্থাপিকা পুরা নাস্তিক,1,religion
হে দেওয়ান বাগীকে হেদাআত দান কর ।। যদি হেদাআত না থাকে তাকে ফেরাউনের চেয়েও নিক্ঋষ্ট মৃত্যু দান কর।।।।।।,1,religion
বইশা তুরে পুন্দাইব মাগি,1,religion
নাস্তিক কুতার বাচ্ছা,1,religion
পাগলা যদি ল্যাংটা হয়ে ওলি হয় তাহলে তুই ও ল্যাংটা হয়ে যা ভন্ড কোথাকার পাজলামি করার আর জায়গা পাসনা হারামজাদা তোর দুই গালে মন চাইতেচে সবার সামনে টা বাড়ি মারি,1,religion
এই সালাকে আগুনে পুড়িয়ে মারেনা কেনো?,1,religion
বন্ড৷ তুই৷ সালার৷ পুত,1,religion
আহলে খবিশদের উপদ্রব বড় বেড়ে গেছে।।সালারা অনলাইনে যত বাহাদুরী।পারলে সরাসরি বস না কেন??,1,religion
দেওয়ানবাগী একটা বাইনচুদ!আর ভাই আপনাকে বলছি আপনে ও একটু ভাল হন,1,religion
সারা জীবন শুনলাম চুল ছোট রাখা সুন্নাত এই হারাম জাদা বলে চুল লম্বা করা সুন্নত হালা শালার পুত,1,religion
ভন্ডা মাগির দালাল,1,religion
মনে হচ্ছে তুই পড়া লেখা সবার থেকে বেশি করে ফেলছিস সালার ভন্ড,1,religion
এই মাদার চোদ কে ইচ্ছা মতে পিটানো হয়েছিলো তার আস্থানা নারয়নগঞ্জ থেকে ভেঙে দেওয়া হয়েছিলো । আমারা ওদের পিডাইয়া এলাকা ছাড়া করছিলাম ।,1,religion
টা খানকির বাচ্চা আর একজন হল মানুষ,1,religion
মাগির পুত রে পাইলে জুতা পিটা করতাম।দেওয়ান বাগি খানকির পুত,1,religion
তাহেরি মাদারচুদ এই খানকির পুত,1,religion
মুরগী কবিরকে জুতা দিয়ে পিঠানো উচিত। শালা একটা নাস্তিক কুকুরের বাচ্চা।,1,religion
মাদারচুদ পিরের পোলাররে জোতা মার আমারে লো,1,religion
পতিতা মহিলা তুই। তোর মত মেয়ের। পীর মুফতি গিয়াস উদ্দিন আল তাহেরী হুজুরের জুতা মোছার যোগ্যতা গাড়ি মোছার যোগ্যতা তোর নাই জানিস তুই তাহেরী হুজুরের কত জনপ্রিয়তা ব্রাহ্মণবাড়িয়ায় তার ডাকে লক্ষ লক্ষ মানুষ জড়ো হয় সাহস থাকলে নিচে পরিচয় অল্প কিছুদিনের মধ্যে ভিডিও বানানোর রেজাল্ট পাবি। টাকার মেয়ে তুই,1,religion
আববাসিরে জুতা পিটা কর,1,religion
মাদারসূদ অহাবি,1,religion
জোতা দিয়া তোর মার ওতোর বাবার কপালে পিটাবি খানকির বাচা রা তোর মাগো কুতা দিয়াা চোদাবো,1,religion
দেওয়ানবাগীর হোগামারার শেষ,1,religion
শালা গাঁজাখোর রাতের একটা বাজে যদি তুই ওয়াজ করস তাহলে লোক গুলো ফজর নামাজ কিভাবে পড়বে তুই প্রমাণ হল তুই দে মাজার পূজারী,1,religion
তাহেরি একটা রাম ছাগল,1,religion
আজাহারি আবেহালা বনড আবুজাহের ইহুদির নাছারা ইবলিস সইতানের দালাল,1,religion
এই বোকাচোদা এখানে তাহেরীর কি আছে,1,religion
আরেক মাগি ফোন করে বলে সে নাকি হজ্জে গিয়েছিল দেখে এসেছে লোকের মাছ আর কিনা কি বিক্রি করছে এই বিষয়ে প্রশ্ন করেছে মৌলানাকে আপনারাই বলেন মাগি কি হজ্জের নিয়তে গিয়েছিল,1,religion
হাপিজুর রহমান বনড হালার পৌতে বেদয়াতি আনতাজি আনতাজি কথা বলে চিনতা করেনা যে এখানে আললাহর ওহি কি আছে না নাই,1,religion
তুমি কি মানুষ না কি না কুত্তা দোয়া করি তর ইওটিভ এর উপর টাডা পরক।,1,religion
সামনে কতগুলো পাগল ছাগল নিয়া শালার পুতেরা করল এ জানোয়ারের বাচ্চা হজে গিয়ে মানুষ ন্যাড়া করে এটা কি আবুজেহেলের না আল্লাহ রাসূলের,1,religion
মাদার চুদে কই আছে,1,religion
মাদারচোদের বাচ্চা,1,religion
ভাইয়া আপনার ইউটিউব চ্যানেলে যত ভিডিও আপনি পোস্ট করেন সেগুলো আমি সবগুলাই দেখি আসলে আপনার ভিডিওগুলো আমার খুব ভালো লাগে এখনো যে দেওয়ানবাগী নিয়ে কিছু বলছেন না কে এগুলো দমন করবে বলেন চলেন আমরা একই সাথে মিলে দেওয়ানবাগী কুত্তার বাচ্চা কে হত্যা করার কোন পরিকল্পনা নেই এই কুত্তার বাচ্চাকে হত্যা করলো হয়তোবা আল্লাহ তাআলা আমাদেরকে জান্নাত দিতে পারে জীবনে তো অনেক গুলি করছে না হয় এই কুত্তার বাচ্চাকে হত্যা করে আরো গুনা করবো তাও এভাবে ইসলামকে নষ্ট হতে দেবো না আমার সাথে কে কে আছেন বলেন,1,religion
তোদের আর কি বলে গালি দিবো তোরা তো এমনিই জারজ সন্তান তোদের কপালে হেদায়েত আছে কি না আল্লাহই ভালো জানেন,1,religion
নাস্তিক কের বাচ্ছা আল্লাহ আপনে আমাদের হুজুকে কবুল করেন আমিন,1,religion
এই খানকির পোলা তূই জারজ সন্তান,1,religion
এই মাগি তর চেহেরা দেখা আমরা দেখতাম তাহিরি বৌউ সুন্দুর তাতে তর জলন হয় কেইন তুই তাহিরি সাথে বিবার কথা ছিলনিকি?এই ভিডিয় কয়রা কত লাখ কাময়লি মনে হয় তুই কোনো ওহাবি দালালের মেয়ে তুই তর মতন আর কয় জনেই বারহয়ছে ছুন্নি আলেম দের বিরুধে এই ভিডিয় দেখিয়া শোদু ওহাবি সুব খুশি হয়ব,1,religion
সব পাগল,1,religion
এই মিডিয়ার কুত্তার বাচ্চা জারজ কুলাঙ্গার তুই সব আলেমদের দুই এক সেকেন্ডের কথা কেটে সবাইকে ভন্ড বানালি তুই কি ফেরেস্তা।,1,religion
শালার আজকাল ইসলামের ওয়াজ নিয়াও ইউটিউবে ব্যবসা শুরু করে দিয়েছে এদের মতো বাটপার কিছু লোক। শুনো চান্দু বেশি ডলার কামানোর আশা কইরোনা পরে কিন্তু পাবলিক যখন আন সাবস্ক্রাইব করা শুরু করবে তখন সব বাটপারি শেষ হয়ে যাবে। তাই বলছি হেডলাইন দিয়ে গিয়ে বুঝে শুনে দিও। মুর্খের মতো দিওনা।,1,religion
লাভ ইউ ভাইয়া এই চুতমারানী পোলারে অনেক আগেই চুদা উচিত ছিল ধন্যবাদ পাশে আছি সবসময় 😍😍,1,religion
রেন্ডির বাচ্চা ভিডিও বানাবি না,1,religion
তোর ইউটিউব চ্যানেলে মুতি ছাগল কোথাকার,1,religion
ভণ্ডদের ধরে জবাই কর ল্যাংটা করে পাছায় আলকাতরা লাগা । কালা কুত্তার ঘু খাওয়াও । ছেঁড়া জুতার মালা গলায় পরিয়ে কিলোমিটার ঘুরাও। আদর করে কাঁচা গোবরের তৈরি রসগোল্লা খাওয়াও। এদের জবাই করা উচিৎ। মূর্খ গরু ছাগল ছাড়া এদের কাছে কেউ যায় না। এ সব ভণ্ড মূর্খরা পারে না এমন কাজ জগতে নাই। এদের আখড়াগুলো আগুন দিয়ে জ্বালিয়ে দেওয়া উচিৎ।,1,religion
নাস্তিকের মারে চুদি নাস্তিক খান্কির পুলারা ওগো জুতাদিয়া বাইরান দরকার খান্কিরর পুলাগো পাইলাম না সাম্নপ পাইলে জব দিতাম,1,religion
রাখ তোর ভিডিও সালা আবাল,1,religion
তর মত কুত্তার কথা না শুনাই ভালো,1,religion
মিথ্যাবাদী শয়তান বানোয়াট কথা বলে সাধারণ সরল মানুষগুলোকে ধোকা দিচ্ছ মনে রেখো অাল্লাহর দরবারে দাড়াতে হবে,1,religion
কোন ইসলামে আছে মেয়ে এসে য়উ টিউব এসে কথা বলবে আর তাহেরি মেয়ে দের সাতে খারাপ কাজ করে তাকলে তার দলিল দেখাতে পারে তুর আরে তুই ত কাপের তর মা বাবা কে বলিস তুই একটা বিয়াদপ বাচ্চা,1,religion
শালা তোকে এই খানে হেদায়েত এর কথা বলার জন্য বসিয়েছে কারো নামে কুট উক্তি করার জন্য নয়,1,religion
এই কুত্তা ওদের দালাল,1,religion
বাটপার খানকির পুলা,1,religion
ওরে জুতা পিটা করার দরকার ছিল ।সালা ভন্ড,1,religion
তর মারে চুদি মাদারচুদ তর বয়স কত তুই বুঝিস কি তর বাল ওঠছে নি খানখির পুলা তরে কি গিবত করার জন্য আনছে তুই নিজেরে বক্তা ভাবছ কি করে তুই লোকের চুদা,1,religion
হে আল্লাহ এই নাস্তিক মেয়েটাকে তুমি হেদায়েত করো,1,religion
ভাই মিনিট দেখার পর আর দেখতে পারলাম না মাথা গরম হইয়া গেছে। মনেচায় গালিদেই দেওয়ান মাগি😡রে। মাথা ঠন্ডা হইলে বাকিটা দেখবো😡😡😡😡😡😡😡😡😡😡😡😡😡😡😡😡😡😡।,1,religion
তালি এই জায়গাটা হইছে এই হালার ঐ জায়গাটা😂,1,religion
মাদারচোদ তুই কাকে ভন্ড বলিস। তুই নিজেই একটা ভন্ড।,1,religion
সব গুলি ছাগলের তিন নাম্বার বাচ্চা আহলে খবিশ সালারা ভন্ডের দল এরাই প্রকরিত শয়তান,1,religion
এই জারজ মাগি তুই তোর বাবার সাথে সেক্স কর,1,religion
তুই কয় বাপের জর মিলা হারমজাদা। ভুজে সুনে কথা বলিস। ভিডিওটি ডিলেট কর। পুরা ওয়াজ সুনো বিয়াদব,1,religion
ওই খানকির পোলা কি ভিডিও,1,religion
দূর সালারপুত সালা ইসলাম বুজচ নি,1,religion
এই খানকির পুলা তর চেনেলের মাইরে চুদি তুই কি চিনিস,1,religion
ইতে সিউর মদ খেয়ে মাতাল হয়ে উল্টোপাল্টা কথা বলে।এতোই মাতাল যে কথা বলার জোর পাচ্ছে না।কুত্তার বাচ্চা।,1,religion
একজন হুজুরকে বলার সুযোগই দিচ্ছে না ঐ চারজন কুত্তার বাচ্চা,1,religion
দুর কুত্তার বাচ্চা,1,religion
হালা আবালের আবাল লেখছেকি আর দেখালো কি জানুয়ার,1,religion
শালার মাজার পুজারি বেদাতির গুষ্টি,1,religion
ঐ মাদার চোদেরা ভারত গরু কুরবানী নিষিদ্দ করছিল মুরগী চুরের বাচ্ছা খানকির পোলা আর সামিয়া তুই খানকি ইসলামের কিছু জানা আছে তর তর মাংগের ভিতরে সরাসরি যদি রড ডুকানো হয় তাও আমার মনে শান্তি আসবনা কারন তরা কাকে অপমান করছিস এশিয়া মহাদেশের সাখুল হাদিস হলেন উনার বাবা,1,religion
তুরা বাইচোদ,1,religion
নাস্তিক কে জুতা পিটা করে বাংলাদেশ থেকে বিতাড়িত করা হক,1,religion
চারটে কুত্তা একটা মানুষকে ধরেছে কুত্তার ঘেউ ঘেউ শব্দ তে মানুষের শব্দ ক্ষীণ হয়ে আসছে,1,religion
কুত্তার বাচ্ছা তুই আব্বাসি কে নিয়ে এমন করলি কেন,1,religion
এই খানকির পোলা মুরগি কবিরকে কেনো টিভি তে আনা হয়?,1,religion
তোমার কোন বালটায় ক্ষমা করবে না? তুই হালা তো ভন্ড,1,religion
কুত্তার বাচ্চারা পারলে তোদের পরিচয় দে।।।।,1,religion
খানকির পুলা তোর বাপ ঠিক আছে না কি সনদেহ আছে আগে বাপ ঠিক করিস তার পর হাফিজুর ভুল দরিস খানকির ছেলে,1,religion
কুতার বাচারে মাইরা লামু,1,religion
কিরে এডমিন তুর চোখ কান কি কানা জারজের বাচ্চা তোদের জন্ম ঠিক নাই,1,religion
তোর মত কুত্তা একটা বেয়াদব।হাদিসে বলেছে কি?আর বলদে বলে কি?ছাগল কোথাকার,1,religion
তাহেরি তে পাগল তাহেরি তে ছাগল,1,religion
কিরে পাগল তুই নিজেই ভনঠ,1,religion
এই কুত্তার বাচ্চা তুই কি অলিপুরিকে চিনিস ? যাকে ভিডিওতে অলিপুরি বলছিস সে কি অলিপুরি বেটা ছাগল,1,religion
মাগির পোলা গাজা খা তুই তুই তো কিয়ামতের আলামত,1,religion
তোরা কুরাআনের কি বুঝো মুনাফেক দেওয়ান বাগি কুওার বাচ্চারা,1,religion
এই কুলাঙ্গারের বাচ্চা 😡😡😡হাফিজুর রহমান হুজুর তো খোদা দাবি করে নাই তুই মিথ্যা লেখলি কেন বেইশ্যার মাগির পোলা তরে পাইলে বুঝাই দিতাম কোন জায়গা আঘাত দিলি,1,religion
মূর্খ শালারা নাস্তিকের বাচ্চারা হুজুরকে তো কথা বলার সুযোগই দেয়া হচ্ছে না আর জানিনা এই নাস্তিক কি ধর্ম পালন করে কোন ধর্ম ব্যাপারে তাদের কোন আইডিয়া নাই আমি ওইখানে উপস্থিত থাকলে শাহরিয়া কবির কে ঘুশি মার তাম,1,religion
তোর মারে আর তোর বোনের বিয়ে কর খানকির পোলা। বাংলাদেশ আসে বল এ কথা গুলো।,1,religion
এডি হলো কুটটার বাচচা,1,religion
এটা একটা কুত্তার বাচ্ছা এর চামচা ও অনেক মানুষ কিছু বলতে পারেনা এর চামচাদের ভয়ে ভাই আপনি এই ভাবে চালিয়ে যান মানুষ এই কুত্তার সম্পার্কে সচেতন হতে পারবে,1,religion
আরে সালি তুই কি জানিস তাহেরির ভিতরে কি আছে সালি তুই তো ইসলামের নামে কলঙ্ক,1,religion
কুততার বচচারা পগল,1,religion
তাই মাগি থাই মাও মাগি,1,religion
এই সালারপুত হলো মাগির দালাল এনায়েত,1,religion
শালার পুত মুখে লাগাম দিয়া কথা বল লজ্জা করে না তর বাপের বয়সের একজন দারিয়ালা আলেম কে গালাগাল করস,1,religion
শালা লুচ্চা বেটির বনির দুধ ছবি দিয়া তুই বিদ্যান সাজতে চাস।শালা লুচ্চার বাচ্চা,1,religion
বড় বাটপার তো ব্যাটা তুই কোন হাদিসে আছে মানুষের বিরুদ্ধে গীবত গাওয়া এবং বদনাম বলা আগে নিজে লেখাপড়া করে তাদের মতন হয়ে তারপর তাদের বিরুদ্ধে বলতে আসবি তোর তো ব্যাটা এই চেয়ারে বসার যোগ্যতা এখনো হয় নাই,1,religion
হাওড়া মাগির জাউরা পোলা তোর মারে চুদদে কইরাম ফালাফালা আজকে আমার দিনটা ভালা । চোদানি মাগির পোলা বেধানি মাগির পোলা কই গেলিরে কই গেলি তোর বোদার ভিতরে গেল আমার সোনার কলি খান্কি মাগির পোলা তোর মার বেদাকালা তোর মারে চুদদে লাগে না ভালা তোর প্রতিবন্ধীর আম্মুটারে আমি সুদি। তোরে কোন শালায় মুখস্থ ওয়াজ শিখাইছে। তুই জানোস না গীবত গাওয়া ইসলামের দৃষ্টিতে কি। কোরান হাদিস নিয়ে আলোচনা কর। শিশু বক্তা কিয়ামতের লক্ষণ।,1,religion
বাল পাকন বাচ্চারে ইসটেজ থেকে লাতি দিয়া নামা,1,religion
শালা তুই বাটপার,1,religion
অজু ছাড়া বাগিচায় মাদারি,1,religion
ভন্ডদের বিরুদ্ধে বললেই নাস্তিকদের গা জ্বলে উঠে শালাকে জুতা পেটা করে বের করা দরকার ছিলো কত বড় সাহস হুজুরের মুখে মুখে তর্ক করেন,1,religion
নাশ্তিকের বাচ্চারা,1,religion
জুতা মার সালারে,1,religion
এই নটির পুতেরে জুতা বাইরে,1,religion
হায়রে মূর্খের বাচ্চা তুই তো ছাগলের তিন নাম্বার বাচ্চা না খাইয়া নাছোচ,1,religion
দেওয়ানবাগী একটা কুত্তার বাচ্চা,1,religion
তর মার হানগা খানকি।,1,religion
হাইওয়ান কুত্তা বাচ্চা,1,religion
কোন মাদারচোদের ভিডিও আপলোড করস শালার পুতেরা মাদারচোদেরা ভিডিও বানাস কিল্লিগা তোরাই ভিডিও ভন্ড হুজুরের ভিডিও নাচ কীর্তি তাহেরী গিয়াস উদ্দিন তাহেরী,1,religion
তাহেরির পাছায় গরম ডিম দেয়া দরকার,1,religion
এই মাগি বড় নাসতিক,1,religion
বাংলাদেশএ এত শয়তান কুতায় তেকে আসল নাস্তিক গুলা,1,religion
সুদু কুত্তার বাচ্চা বললাম বাকিতা জদি তুরে সামনে পাইতাম তারপর বলতাম,1,religion
আগে তোমার পুটকি খুলছে নি? 😆 বাঞ্চদ,1,religion
জুতা পেটা করা দরকার সালা ভন্ডামি করছিস আর বলছিস আমি মা ফাতেমার সামী তুইতো মা ফাতেমার জুতার সমান দামনাই সালা,1,religion
তাহারী হালার পো,1,religion
পতিতা রা এরকমি বলে।,1,religion
খানকির বিচার চাই,1,religion
খানকির পোলাগো ধইরা জুতা দিয়া পিটাইতে হবে আগে প্যাট মোটা হালারে প্যাট ফাইরা সব ভুরি বের কইরা ওগোরে যত গুলা মুরিদ আছে সবাইরে খাওয়াইতে হবে,1,religion
এ অভাব হয়ে যায় সালা বাটপার তরে কত বার দুলাই করলো,1,religion
কুততার বাচচা,1,religion
মাগির পুয়া তুরে এস্টেজে আনছে কে ? আবাল চুদা,1,religion
শালা দেওয়ানবাগীকে চামড়া ছিল্লা লবণ আর মরিচগুড়া শরীরে ডোলা দেওয়া দরকার।। কুকুরের ছাও একটা। ভিডিওটি বানানোর জন্য অনেক ধন্যবাদ। দরকার ছিল তাকে নিয়ে ভিডিও করার। মেজাজটাই খারাপ হয়ে গেল তার হাদিস শুইন্না😡😡😡,1,religion
তাহারী তকে কি কিছু করছে নাকি না তর মা সাথে কিছু করছে মাগির ঘর মাগি তর মারে চুদি,1,religion
এইকুত্তারবাচ্চার শারিয়া নাস্তিক জুতার বারী দিন,1,religion
খাংকির পোলা বক্তা তুর জন্ম এইদেশে না এইদেশ অলি আল্লাহর দেশ তুই অলিদের বিরুদ্বে কথা বলছ,1,religion
কুত্তার বাচ্চাকে ফাসীতে জুলাউ তার পরে অদের পাছাই আগুন ধরিয়ে দাও,1,religion
চেনাল ওয়ালা ভাইকে বলছি ! আপনার মত অনেক বড় বন্ড কুত্তা হাফিজুর এর বয়ান শুনে আজ পাচ ওয়াক্ত নামাজি। আপনি বড় ভন্ড।,1,religion
খানকির পোলারে জোতা মার,1,religion
শালা বাটপার,1,religion
হায় রে লুচ্চা তুই একটি পতি তা,1,religion
হুজুর ও ভন্ড জনগন আবাল। মাধারীরসুদ,1,religion
জন নাস্তিক এর জন্য জন মমিনুলহক এই যতষষ্ঠ এই গোলারে পিটানোর দরকার,1,religion
তুই হলে মাদারচুত হুজুর,1,religion
সালাগু উপরে গজব পরেনা কেন।,1,religion
এসব খানকির পোলাদের ওয়াজে হুজুরের পাশে বসায় কে,1,religion
কুত্তার বাচ্চাদের ফাঁসি চাই,1,religion
এরাই জঙ্গি,1,religion
মাদার সুদ,1,religion
তিন মাদারচুদ বসছে এক মাগীকে নিয়ে।,1,religion
কিয়ামতের আলামত বাবু তুমি তো অনেক চোট তাহিরি হুজুর যেই লিংক এ ব্যাট। সেখানে তো তুমি বল‌ও ধরতে পারবা না। আগে বড় হ‌উ তার পর বয়লো। বেয়াদবের গড়ের বেয়াদবের বাচ্চা,1,religion
পাছার ভিতরে একটা বাঁশ ঢুকিয়ে দিয়ে হেইও হেইও করলে ভালো লাগতো ।,1,religion
বেজম্মা দেওয়ান বাগি,1,religion
বন্ড হিসেবে এঁরা পরতিতো কোতার বাচচা,1,religion
চুদনার পো খানকির নাতি তুই কাফের। মানুষের ঈমান নষ্ট করছ কেন। হাফিজুর রাহমান সিদ্দিকির সম্পর্কে কোনো বাজে কথা বলবিনা। যদি বলস তাহলে ধ্বংস হবি।বুঝে শুনে টাইটেল দিছ গাধার দল।টাইটেল চেন্জ কর।কিয়ামত তোরাই অানতেছত টেনে।,1,religion
যেই খানকির পুলারা মাজারে খারাপ বলবে ওর মারে কুত্তায় চুদে জন্ম দিছে,1,religion
আল্লাহ এসব নাস্তিকদের উপরে গজব দেক!!,1,religion
মাদারচোদ তুই ভন্ড তুই কুত্তার বাচ্চা ভন্ড কুত্তার বাচ্চা তোরে পাইলে জুতা দিয়া বাড়ি গিয়ে শিক্ষা দিমু,1,religion
তাহেরি কে দিয়া তরে পুটকি মারামু মিতা কথা বলার জন্য,1,religion
শালারে কুত্তার বাচ্চা বললেও কুত্তার অপমান হবে,1,religion
এক হাংকি সাথে তিন নাস্তিকের বাচ্চা কুত্তারা জীবনেও বুঝবে না,1,religion
এরকম জানোয়ারদের আগুনে পুড়িয়ে মারা উচিত,1,religion
বালপাকনা।,1,religion
শালার ফুত ভয়ে নাটক শুরু করছে।,1,religion
তাহেরি একটা ছাগল পাগল ওর মাথায় হাতুড়ির বাড়ি দেওয়া উচিত,1,religion
ভাই৷ ওরা৷ পাগল৷ আর৷ কিছুই৷ না৷,1,religion
খানকির ছেলে তোর বোউরে চুদি মাদারচোদ অশিক্ষিত মুরখ বর্বর ফকিন্নি ছোটলোক গরিবের চোদা তোরে যদি সামনে পাই তোর গোয়া দিয়া রট ডুকামু আর বাইর করমু,1,religion
একমাএ আবালচোদনরাই এই ধরনের মন্তব্য করতে পারে আজহারি হুজুর কে নিয়ে।,1,religion
আল্লামা মামুনুল হকের জুতাদিয়ে তিনটা পুত্তা ও একটা কুত্তির গালে মারতে চাই।,1,religion
এই খানকির বাচ্চারা তোরা আমার আল্লাহর কোরআনের যে আজকে কষ্ট জাহান্নামে জ্বলবে আগুন জ্বলবে,1,religion
ফাটা কনডমের অবৈদ জম্ম মাদারচুদ ক্যারচা চুদা তোর ওয়াজ শুনা জায়েজ নয়,1,religion
পাগল এইডা কইত্তন উজাইছে,1,religion
তোকে চুদব,1,religion
মাদারচুদের কথা শুনে মাথা ঘুরে যাচ্ছে।এই মাদারচুদের কোনো আইনগত ব্যবস্থা নেওয়া হয়না কেন।,1,religion
এই নাস্তিক গুলোর ফাসি চাই,1,religion
আসল দাজ্জাল আসার আগে অনেক ছোট বড় দাজ্জাল আসবে দেওয়ান মাগি ওই রকম ছোট এক দাজ্জাল ওর কাজ ই মানুষকে জাহান্নামে নেওয়া। এই শয়তানের চামড়া ছিলে লবন লাগিয়ে জীবিত অবস্থায় ঢাকার রাজপথে টাংগিয়ে রাখা উচিত৷,1,religion
যারা শুনিতেছে তারা কি ডিজে পার্টিতে গেছে!!!!! জুতা পিটা করেনা কেন হারামজাদারে,1,religion
তুই ইসলামের কি বজছ মাদার চোদ আলেমদের গিফদ গাছ,1,religion
জুতাপিটা করা উচিত,1,religion
তুইতো সালা ভন্ড মুনাপিক কাপের,1,religion
মাননীয় পাবলিক আমি এই চার নাস্তিককে মাঝ নদীতে নিয়ে পোন্দাতে চাই!!!,1,religion
কুত্যার বাচ্চা,1,religion
দিছে যারা তারা কি দেওয়ান মাগির মুরিদ??,1,religion
গাজা খোর শালা,1,religion
নটিমাগি নাস্তিক এরা হুজুরে সামনে মাথাই কাপড় দের না বেরাদব বুদ্ধিজীবী এরা।,1,religion
সালায় গাজা বেশি খাইছে,1,religion
তুই এক নাম্বার ভন্ড। সালা তোর চাইতে পাবলিক ভাল বোঝে।,1,religion
এই মাগি তুই কি দেওয়ান বাগির চাম চামী করছি লটি তোর জন্য আমার মুখটা খারাপ হলো শয়তান ছেরী,1,religion
বন্ডর ঘরের বন্ডর বাচ্চা ভন্ডদের কারণে বাংলা দেশটা ধ্বংস হয়ে গেছে ভন্ডদের যেদিন ফাঁসির কাষ্ঠে ঝুলিয়ে মারা হবে সেদিন বাংলাদেশে ভন্ড মুক্ত হবে,1,religion
লোপার পুটকিতে গরম ডিম দে,1,religion
চার কুত্তা একটা মানুষ,1,religion
এই চ্যালেনের সালা পাগল সবাই ব্লক মেরে দেন,1,religion
আপনি হুজুর একটা হারামজাদা,1,religion
তাহেরীর মার পেট ভালো ছিলনা ও একটা জারজ সনতান,1,religion
তুই সালা ভনড,1,religion
পুরান পাগলের ভাত পাইনা নতুন পাগলের আমদানি শালার পাগল,1,religion
সালা মুরগি চোর তাহলে বঙ্গবন্ধুর হত্যা কারীকে পুরস্কার দেওয়া উচিৎ তোর মতে,1,religion
জানোয়ার হাসিনার জন্যই আজ মুরগী কবির এই যায়গায়,1,religion
কিছু ইউটিউবার কুত্তার বাচ্চারাই হুজুর দের নিয়ে ফেতনা ছড়াই,1,religion
বুঝলাম এ কি কোন কিয়ামতের আলামত এত ছে ।ট ছেলে এসব বলা ঠিক না তাহিরী শালার কী বলতাম এসব বাংলাদেশ টা কী হল কেউ কখন ভাবেনি এমন জুগআসবে,1,religion
কিরে এডমিন তৃর চোদ্দ গুষ্টি কপালে জুতার বাড়ি দেয়া দরকার,1,religion
দেওয়ান বাগ হল কুওার জন্ম,1,religion
কোথাই থেকে বের হয়ে আসে অসুস্থ গুরু ছাগল,1,religion
তাহেরি ছাগেলে একটা কমেডি।,1,religion
নাস্তিকের বাচ্চা নাস্তিক।,1,religion
তাহেরী খানকির ছেলে।,1,religion
বাস্টার্ড টা ত বলেছে সে নাকি আল্লাহকে হাত ধরেছে বাচাইয়া দিছে নাউজুবিল্লা উনা ভক্ত্রা কি চুষে এসব দেখেনা ?,1,religion
দেওয়ানবাগী খানকির পোলা,1,religion
তাহেরি আসলেই বন্ড,1,religion
সালা কুওার বাচচা,1,religion
! রাব্বুল আলামীন নিজেই চিন্তিত! 🙄 শালা কি গাঞ্জা খাইয়া টাল হইছে নাকি টাল খাইয়া গাঞ্জা হইছে 😂😂😂😂,1,religion
মাগির পুলারা তাহেরির বিরুদ্ধে খারাপ বিডিও করচ কেন সালারা মালাউন ইসলামের সপরকে কি জানচ তোরা বাসটাড এর দল,1,religion
না‌স্তিক এর বাচ্চা সালারা,1,religion
তাহেরী মনে করে কত বড় বক্তা জানি এই শালা কোন মানুষের জাত না আবার মিজানুর রহমান আজহারী কে কাফের শালা তুই বড় কাফের তোর মত তাহেরী তোর মত তাহেরিকে জুতা পিটা কইরা এই বাংলাদেশ থেকে বার করা দরকার তাহেরিকে সবাই আমরা এই কাজটা করলে মনে হয় ভালো হয় কারণ আমাদের মাঝে এরকম বক্তা আমাদের দরকার নাই মানুষের সাথে কথা বলে কিভাবে একই ভঙ্গিমায় কি করে কি ফাজিল এসব মানুষ দেইখা আবার কিভাবে এগুলা দেখে আমিতো নিজেও ভাবতে পারিনা আবার বলে আমি এসব বললে কি আমার গুনাহ হবে শালা তাহেরী তুই মরলে,1,religion
এই চার লোককে জুতা মারো কুততার বাচচারা জুতা মারো চার জনের মুখে,1,religion
কিরে বোকাচোদা তোকে কি পাগল কুত্তা কামর দিছে নাকি বলছিরা জিকির না করে সেলুন দোকান খুল তাওতো ভালো ধান্ধা করবি,1,religion
ভন্ড আযারি,1,religion
খানকির পোলারা সব এক সাথে হুজুর কে ইনসাল্ট করছে,1,religion
বেসসা মাগি লটি সিনাল তোকে সুয়োর দিয়ে চোদা উচিত লটি সিয়োর খানকি মাগি তোর ভুদা ছিরে দেওয়া উচিত লটি খানকি সাওয়া চুদা বেসসা মাগি লটি খানকি সিনাল সি থু থু থু থু থু থু থু সালা মাগি,1,religion
হায়রে ওয়াবির বাচ্চা এখানে অপমানিত কোথায় হলো। আসলে তোরা হয়লি এজিদের বংশ দর নাহয় ইহুদিদের দালাল সালা এডমিন,1,religion
তাহেরি দেশ ছার তুর জাতেরে ছোদি মাদারে বাচ্চা,1,religion
আবে হালায় কয় কি মিজান নাই একটা বক্তা আর তুই একটা ইউটিউবার তোরা দুনিয়াতে খালি ভন্ড চিনলি মুনাফিক চিনলি না,1,religion
কুত্তার বাচ্চারে আল্লায় গজব দেয় না কেনো,1,religion
তাহেরি তর পাছায় আক্কে অলা বাশ দিয়া ডিগ্রি তাপমাত্রায় রাকতে অইবো তাইলে তোর বসেন বসেন জিকির এর ভুত চলে জাইবো শালা ভন্ড তাহেরি তোর মতো তাহেরি মিজানুর রহমান আজহারির জুতা বহন করার জগ্যোও রাখিস না,1,religion
ঐ হালারা মেয়াদ উত্তীর্ণ গাঁজা খাইছে 😡😡😡😡😡😡😡😡😡😡😡😡 এদের পাছার মধ্যে পদ্মা সেতুর পিলার ঢুকানো উচিত,1,religion
হিজরার মতো ভাব করে সালা পাগল,1,religion
কাপের কে লাতি মারি এবং গোয়া মারি,1,religion
জুতা মারা দরকার বুইড়া শালা মুরগি চুর,1,religion
জুতা দিয়ে মারতে ইচ্ছা করছে এই নাস্তিকের বাচ্ছা কে,1,religion
তাহেরিত তার ওয়াপকেনিয়ে ছবি তুলেচে তার ওয়াপকেদিয়েত বেবসা করতেচেনা আর তুর অবিবাবকত মাগির দালাল তুকেদিয়ে বেবসা করে বেসসা পারার মাগি তুই,1,religion
আদার বেপারি বেটা জাহাযের খবর নেচ সালার পুত,1,religion
দেওয়ানবাগী চুলটা করে গো আবার মুখ আর দেওয়ানবাগীর মুরিদ রয়েছে তাদের কে উল্টা করে চুদল,1,religion
তুই বালে পাংনা তুই হালা জানুয়ার,1,religion
শালাদের মোখে মোতা দরকার,1,religion
সালায় পাকনামি কইরা শেষে অপমানিত হইলো হালা খালেক,1,religion
বুঝছি সালারপুতে চুদতে হবে। অল্প বয়সে বাল পেকে গেছে।,1,religion
এই উপস্থাপিকা একটা মাদার চোদ ! কবিরকে যদি কখনো সামনে পাই থুতু দিলেও দিবো,1,religion
হালারে দরি সবাই জুতা মার,1,religion
এরা সব গুলো শয়তানের বাচ্চা,1,religion
এই নাস্তিক মাগি রে তাহসিনেশন এর কাছে পাঠানো হোক,1,religion
এই শালা মাঝার পুজারী তুই ভন্ড শিয়র।,1,religion
আচ্ছা ওই খানকির পোলা রে ক যদি বাংলাদেশের অফিসে মসজিদ নামাজ পড়ার স্থান থেকে হিন্দুদের জন্য দেওয়া হয় না তাহলে আর একটা কথা ভারত বা অন্যান্য খ্রিস্টান দেশে অফিস গুলোর মধ্যে কি নামাজের জায়গা আছে যে কথা বলেছে নাস্তিক মুরতাদ এবং ওর মা ও সৎ ছিল এবং সে অসৎ এবং জারজ সন্তান,1,religion
নিজেরাই কাবা ঘর বানিয়ে তোরা হজ্ব পালন করিস জারজ তোরা অমানুষ,1,religion
তোর কি মাগী,1,religion
কিছু কুত্তার বাচাচা করেছে,1,religion
কুকুরের বাচ্চা কবরে গেলে জাহান্নামে যাবি,1,religion
অকে দোলাই দিয়ে বেৰকৰে দেউয়া হক অই শালাৰ বাচ্চা মাজাৰেৰ বন্ধমি পিৰ,1,religion
ছাগল এর বাচচা শয়তানের বড় ভাই😂😂😂,1,religion
কুত্তার বাচ্চা তোর মত ভন্ডদের কাছে বানানো হাদিস ছাড়া কিছু নাই,1,religion
দেওয়ান বাগী হালা একটা গাজা খোর,1,religion
বান্দরের বাচ্চা ভন্ড তোর মায়েরে বদলাতে চুদামু,1,religion
উপস্থাপক বেলুন এক্সিডেন্ট এর জন্ম।,1,religion
উপস্তাপিকা ত্রকটা বেস্যা নষ্টা বাকিরা পেরাউনের বংসোদর ত্রদের সব গুলকে জন সমূখ্যে পাসিতে জুলিয়ে হত্যা করা জাতির জন্যো মজ্ঞল,1,religion
জারা ভন্ড বলবে হাফিজুর রহমান কে তারা সেই কুত্তা বাগির মুরিদ,1,religion
নোপা মাগির হাসি দেখে মনে হলো যে কতো ছেলের ধন চেটেছে জন্মর দিক নেই নোপা পতিতা,1,religion
তুরে পাইলে জুতা দিয়া বাইরামু তুই কারে কি বলছত তুই জারজ সন্তান,1,religion
এই ওহাবীর বাচ্চা তাহিরি তর বাপ,1,religion
নাস্তিক আসিফ মহিউদ্দিন কাফির নিজের স্ত্রীকে উলঙ্গ করে পৃথিবীকে দেখিয়েছে এই ভিডিও দেখে সবাই বুঝলেন যে নাস্তিক আসিফ মহিউদ্দিন কাফির শুকর চরিত্রের পুরুষ 😶 । নাস্তিকরা ব্যবিচারী !,1,religion
শালার পুত আরেক বেটার গিবত না গেয়ে বেটার সাথে গিয়ে বাহাস কর তর বাপের বেটা হলে । তাহেরি হুজুর একজন মুফতি আর তুই কি? আর আব্বাসি হুজুরকে বলছ বন্ড শালা তুই বন্ড কোতাকানের পিচ্চি,1,religion
দেওয়ানবাগীর মুরিদরা পাগল।তাদের কিছু বোঝানো যাবে না।এক আল্লাহুই পারে তাকে ধ্বংস করতে।,1,religion
হিতারার মার হেডার অনুষ্ঠান,1,religion
ভাই এই মাদারচুদের কারনে আরামবাগ থাকা যায় না,1,religion
তোর মা রে বোইনেরে পতিতালয়ে দিয়ে টাকা কামা হারামজাদা।,1,religion
যেই মাগীর বাচ্ছারা এরে আনে তাদেরকে কুত্তাপিটা দেওয়া উচিত,1,religion
সালা প্রাটি কবে থেকে শুরু করলো তাহেরি,1,religion
দেওয়ান বাগীর পুটকী দিয়ে গরম ডিম দেওয়া দরকার,1,religion
তাহেরি ছাগলের তিন নাম্বার বাচ্চা।,1,religion
কোন সালারা,1,religion
সালারে কাছে পাইলে জুতা মারমু কুতার বাচা,1,religion
এই সালার পো হাফিজুর রহমান হুজুরের ছবি ভন্ডদের সাথে মিলাইছো কেন।।।,1,religion
ভাই শালা অরিজিনাল এ কুত্তার বাচ্চা,1,religion
তাহিরী খাংকির পোলা এর জলমো নাসতিকের বারিত,1,religion
সালা মাগির পুত দেওয়ান বাগি,1,religion
শালা ইবলিশের খালতো ভাই ভন্ড শয়তান এগুলোর উপর আল্লাহর গজব পরে না কেন???,1,religion
অ‌নেক ভাই ক‌রে‌ছেন যে লোপাকে চুদ‌তে চাই তা‌দের কে বলব ও‌কে চ‌ু‌দে হোল নষ্ট করা যা‌বে না ভাই,1,religion
মুরগি চোরা শাহরিয়ার কবির এই কুত্তারে দেশ থেকে লাথি মেরে বের করে দেওয়া উচিৎ আমার মনে হয় এটা মুজিব হত্যাকারীদের মধ্যে একজন পাশেই বসে আছেন সামিয়া রহমান বেশ্যা কোথাকার,1,religion
কুত্তার বাচ্চা গরে রাস্তায় ফালায়আ কোপানো দরকার,1,religion
ওই হালা তুই কি হুজুর ?,1,religion
কানকি পোলা,1,religion
খানকি মাগির বাচারা তোগরে পাইলে পাথর মাইরা খুন করতাম,1,religion
আরে কুত্তার মতো ভাই রান দরকার,1,religion
তুর মাইয়া তাকলে আমারে বিয়া দিচ। তুর মাইয়া রে নিয়া আমি নাচমু।।।।। বাংলা চুদন দিমু,1,religion
হ্যা অাল্লাহ তুমি এই নাস্তিকদের খেদায়াত করো,1,religion
এসব কথা যারা নবীর বৃদ্ধ কথা বলে তারা মুনাফিকের বাচ্চা তারা মুসলমানের বাচ্চা না ঈদে মিলাদুন্নবী পালন করতে হবে যা না পালন করে তারা কাফের তারা মুনাফেক,1,religion
শালা একটা ভন্ড আস্ত বন্ড,1,religion
আনলাইক করা জন কি দেওয়ানবাগীর ফলোয়ার নাকি!!! কি রকম ব্রেইন আর আই ওয়াশ করে রাখছে সালা ভন্ড দেওয়ানবাগী!!! ক্যারি অন তাহসিন ভাই!👏👏👌✌,1,religion
নাস্তিকের বাচ্চাদেরকে মনে হচ্ছে থাপ্পর দিয়ে কান ফাটিয়ে দেই জাহেলের বাচ্চা জাহেল।,1,religion
https://docs.g,1,religion
নটির পুলারে মারার পওজন,1,religion
সালা বন্ড ।। বেজাল আছে তোর জিন্মে,1,religion
কুত্তা বাচ্চা দের গলায় পারা দিয়া মারা লাগব🤬🤬,1,religion
এক নাম্বারের ভন্ড কুলাংগার মাজার পূজারী মাগী খুর। কুত্তার বাচ্চাটাকে খতম করা উচিত,1,religion
মার খানকির ছেলেকে,1,religion
মাদারচোদ,1,religion
তরে পাইলে তর পিছন দিয়া সুনা বড়ে দিতাম,1,religion
মাজার পূজারী শালাকে সবাই ধরে গাড় ভেংগে দেওয়া উচিৎ,1,religion
তাহেরী মদ খাইছে না না পাগল কুকুর কামড় দিয়েছে,1,religion
হালার পুত তোরাই তো এগুলো বানাস,1,religion
সালায় এক ভন্ড দেওয়ানবাগী,1,religion
আরে পাগল ছাগল জারা খায় তাদেরকে ক জার মাজার তারে কছকে মাওলানা চুদির পুত,1,religion
ফাইজলামি চুদাও না ওয়াজ শেখার আগেই ভন্ডামি শুয়ে গেছো মানুষের গিফত গাও,1,religion
মাগির নাস্তিক কে জুতা মার,1,religion
তুই একটা কুকুরের বাচ্চা,1,religion
কোন কথা কী বুঝায় সেটা বুঝার যোগ্যতাই এখনও হয়নি শাল্লা কুত্তার বাচ্চা আব্বাসী আরও গালি আসতেছে বাকিগুলা আপনারা দেন।,1,religion
ওই শুয়ারের বাচ্ছাটারে জুতাদিয়া পিডাইয়া ওইখান থেকে নামিয়ে দেয়া হোক,1,religion
ওই মাদারচোদ,1,religion
তুই একটা বাইনচোদ মাদারচোদ,1,religion
পাডার বাচ্চাকে জুতা পিটা করলো কেন ভারতীয়রা,1,religion
এই রকম লুকের পাসায় গরম লট লাগাই দিলেও রাগ কমবে না একে ত। এই দেওয়ান বাগি কুত্তার বাচ্চা,1,religion
নাস্তিক কানকিপোলা গোরে এই বাংলাদেরের রাকা হয়েছে কেনো,1,religion
তুই কুত্তা শুয়ার এর চেয়ে নিচে।।।তর অবস্থান।।।,1,religion
ওরা দেওয়ান বাগির ভক্ত না মাল পায়তো তাই জ্ঞান বুদ্ধি সব বিক্রি করে দিছে। আমার দুঃখ হচ্ছে তাদের জন্য যারা মাল পায়না অথচ এই শুয়োরের ভক্ত তারা বেশি ওভাগা।,1,religion
খানকির পোলা তুই ভন্ড তর বাপ ভন্ড,1,religion
আহলে খ‌বিস মাদারচ‌ুদ গুলো কই,1,religion
সয়তানের বাচ্চা আর কোনো কাজ নাই,1,religion
মার সালা দেওয়ান বাগীকে । তুই একটা বার আমার ভারতবর্ষে এস বল এই কথা টা । তোর পিঠের চামড়া কেটে ফেলে দেব। তুই বাঁচবি কিনা সন্দেহ,1,religion
দেওয়ান বাগি না বলে দেওয়ান মাগি বল্লে মানায়,1,religion
সালা বনডো মাদারি,1,religion
আব্বাসী একজন রাম ছাগল।অল্প বিদ্যা ভয়ংকর।,1,religion
ভাই ওই মেয়েক যেখানে পাবেন মেরে ফেলাবেন আমি পাই লে আমি ও মেরে ফেলব আল্লার কসম,1,religion
শালাক চুদা উচিত,1,religion
নাস্তিক এর বাচ্চা কার সাথে কথা বলতে যায়।😂 হুজর এর জুতা পরিস্কার এর যোগ্যতা নাই।😂😂😂,1,religion
সালা দেড় ইন্চি বদমাইশ কুলাংগার তর জন্মের টিক নাই।তর মতন দের ইন্চি বক্তা হলো কিয়ামতের আলামত।কুরআন বলতে কী বুজচ?? বাটপার বদমাইশ,1,religion
শালা শাহরিয়ার মুরগি চোর কে ধরে পিটা ইসলামের নাম শুনলেই চুলকায় বেশি,1,religion
তর মার ভুদা দরকার সব জায়গায় শালা নাস্তিক এর বাচ্চা,1,religion
সালায় মহিলা গু উর্না গলায়,1,religion
এই ভন্ড দের রাস্তায় জনগণের সামনে ফাসি দেয়া ইচিত। হারামির জাতেরা। ইসলামের নাম খারাপ করছে,1,religion
হেতে বন্ড না? হারমীর বাইচ্চা তুরে কোন মায়রে জন্ম দিছে সে মায়ের ও কলংক হারামজাদা তুই বন্ডা তাহেরি ঠিক আছে। সঠিক লাইনে আছে। তুই ঠিক হয়ে জা।হারামজাদা,1,religion
মাদারচোদ এরা কি বলে?,1,religion
উপস্থাপিকা দেখছি নিজেই আলোচক একজন পতিতা এই চারজন নাস্তিক কে ধোলাই করার জন্য একজন আদর্শিক মুসলমান যতেষ্ঠ,1,religion
হাই কুত্তার বাচ্চা ইউটোবার,1,religion
দেওয়ানবাগী ভন্ড খানকির তোর ভোদাটা,1,religion
শালারে ফাঁসি দেন,1,religion
বাবা রা তর মার জামাই নি ভে ভন্ড হালা গুরু,1,religion
সালায় একটা বন্ড,1,religion
ও একটি কুলাঙ্গার,1,religion
এ মাগির পোয়া নাকি মারা গেছে,1,religion
নাস্তিক ধর জবাই কর,1,religion
এইটা খানকা শরীফ না খানকী শরীফ।,1,religion
মিথ্যুক তুই কুত্তা।শিরোনামে কি লিখছচ তুই???বক্তাকে মারছে?? কেনো বক্তাদের ছোট করস??,1,religion
আর মাথাই এটা কি পরছে সালা বন্ডের দল,1,religion
নাস্তিকরা কুত্তার বাচাচা সব,1,religion
শালারে তার শ্রোতারা জুতা মারেনা ক্যান👿👿👿👿,1,religion
এই বেপরদা মহিলা এবং এই তিন নাস্তিককে বাশ দিতে হবে,1,religion
হালার পাচায় 🎍 বইরাদে,1,religion
শিশু বক্তা আনে কুন শালারা,1,religion
পারে না সূরা ফাতেহা বলতে ওরা আবার মামুনুল হকের ভুল ধরে হালার নাস্তিক কতগুলা,1,religion
খানকিমাগী তোর খাজা বাবা আল্লাহর সামনে খুঁজে পাবি ভালো হয়ে যা খাজা বাবার জুতা মারি,1,religion
কবির মাদার চোদ তর কপালে শনি আছে।,1,religion
তিন জনই ইসলামের শত্রু । সাংবাদিক তাদের থেকে বেশি কথা বলে । এরা সবাই কুলাংগার ।,1,religion
চুদির ভাইয়েরে। থাপরাইয়া নামাছনা কেরে ?,1,religion
চার মাগির বাচ্চা তোরা সবাইতো ইসলামি বিরোধী খানকিরপোলা।,1,religion
রুপামাগিকেঘোড়াধনদিয়েচুদতেহবেতাহলেমাগিআলললাহকেনিয়েকোনোখারাপকমেনকরবেনাআমিমালসিয়াপবাসি,1,religion
এই বালপাকনা তুকে ওয়াজ করার পারমিসন কে দিয়েছে তুইত এখনও আদব কায়দাই শিখিছ নাই তুর উস্তাদ বা তুর মা বাবায় কি তরে আদব কায়দা শিখায় নাই বেয়াদবের বাচ্চা।,1,religion
মা গি কে জু তা মারা উচিত,1,religion
সুয়ারের বাচ্চা কে জুটা করা দরকার,1,religion
তুই জারজ হারাম জাদা,1,religion
সালাকে সামনেপেল কেটে ফেলবো তোর যদি দম থাকে তাহলে সামনে এসে বল যে মাঝারে যায় হারাম সালার লাস উঠানার লোগ পাবিনি মাদারচোদ,1,religion
আপনাকে অনেক ধন্যবাদ ভিডিওটা বানানর জন্য সব কয়টা ভনড। কুততার বাচচা,1,religion
লোপা রহমান তোর হাসি তো একজন পতিতা মেয়ের হাসি মত তোর হাসিতে আল্লাহ পছন্দ করবে না আমাদের দেশে আলেম সমাজ তোকে তো ভালোবাসে না তুই এভাবে নিজেকে কি মনে করিস,1,religion
কিছুদিনের ভিতর বিনাশ হয়ে যাবে মাদারচোদ রা সব হলো হিন্দুর চ,1,religion
এরা কুত্তার বাচ্চা।।,1,religion
দুর শালা,1,religion
তর টা দেখেই বুঝাযাই তুই ভন্ডার ঘরের বন্ডা দেওয়ান ভাগীর মুরিদ ছাগলের ঘরের ছাগল,1,religion
দেওয়ানবাগি কে কেউ মারে না কেন? এই সালা চুদির ভাই।,1,religion
এই সালার ভন্ড হুজুরদের গলা জবাই করে ফেলা উচিত,1,religion
নাস্তিক হারমজাদারা,1,religion
এগুলো সব হলো কুকুরের বাচ্চা ওরা ওদের মায়ের পেট থেকে বের হয় নাই এরা কুকুরের পেট থেকে বের হয়েছে,1,religion
গান গাইলো চুদমারানী আবার এটা কে,1,religion
ডিস লাইক দিছে কোন কুত্তার বাচ্চা রে,1,religion
ওই সালা ভন্ড তুই।বক্তব্য ঠিক আছে,1,religion
জুতা মারা দরকার ছিল শালার পোরে মাজার পূজারী,1,religion
এ কি বক্তা না কি। শালা কি ওয়াজ আপলোড দিলি তোদের কে জুতা পিডা করার তরকার।,1,religion
এ জানয়ার এর নাম জানিনা তবে সালা ভন্ধ এ জানয়ার জতু মিলাদ নেতে ছেরেছে সব ভুল,1,religion
খানকি কয়শ বেটার সোনা মুখে লইয়া মুখ এত বড় করলি।,1,religion
কুত্তার বাচ্ছা পয়দা হইছস কয় দিন হইছে।ইসলামের কোন জ্ঞান আছে? শালা জারজ সন্তান সাহস থাকলে ফোন দে,1,religion
দেওয়ান বাগী শয়তান বাপ ভাই,1,religion
এই পতিবিন্ধ তুই চুপ কর ওহাবির কিট নাসক,1,religion
এই শালা শুয়রের বাচছাদের জন্মের ঠিক নাই।,1,religion
দেওয়ান বাগী কুত্তার বাচ্চা জানোয়ার,1,religion
পারলে তার সামনে দলিল নিয়ে বসেন মাদারচোদ,1,religion
নাস্তিক বাচ্চে,1,religion
দুরু গাজা কুত্তার ছাওয়াল,1,religion
শালারে জুতা মার ভন্ড পীর সাহেব,1,religion
তুই একটা বাইনচুদ এই জন্যইত মানুশের দুশ বিচারছ বাইনচুদ,1,religion
দেওয়ানবাগী খানকিরপোলা জারজের সন্তান সরল মুসলমানদেরকে কাজে লাগিয়ে শয়তানের আখড়া বানাইছে। খ্যাংকস ছোট ভাইরা এই ভিডিওটির জন্য। দেওয়ানবাগীর গালে জুতা মারো তালে তালে।,1,religion
ভাই আবার মন্তব্য করলাম।এই শালা দের জুতা মারো আর আমাকেও মারো কারণ আমি কেন দেখলাম,1,religion
কুত্তার বাচ্চা তেদের বিচার আল্লাহ বলবেন,1,religion
ঐ মাদার চোদ মনে হয় মাজার পূজারী ।ও পীর পুজারি । ভাগ সত্য কথা ভন্ড পীরের চেলা ।,1,religion
দেওয়ানবাগির শরিরে মুইতাদেম সালা মাদার ওরে জুতা না মানুষের খাওয়ানো দরকার,1,religion
কুত্তার বাচ্চা জারজ তোর উপর খোদার গজব পরবে দেখবি আল্লাহর বিছার ধিরে ধিরে তুই কুরআনে জুতা রাখলি খানকির পোলা মাথায় টুপি মুখে দাড়ি রাখলি গজব পরবে তোর উপর,1,religion
এই হুজুরের কথা একদম ঠিক সালার বন্ড পিরের বইরারে গার দরে বের করে দেয়া হলো না কেনো ?,1,religion
দেওয়ানবাগি হলো গাঁজা খোর মাগী খোর দেওয়ানবাগি ভন্ড মাজার পূজারি মুসলিম না,1,religion
এই দেওয়াইননার বাচচা তোরে 🔨🔨🔨🔨 তোরে কুততা পিডা দিমু,1,religion
সালা বাংলা বুজিস জানুয়ারের বাচ্ছা আগে পুরো ওয়াজ টা সুন তার পর বলেন ওকে,1,religion
দেয়ানবাগির মাইরে চুদ,1,religion
এই কুত্তার বাচচা কে কুপিয়ে কুপিয়ে মারা হোক,1,religion
তোর বয়স কত দিন তুই কোন কোন কিতাব পড়েছিস এই অল্প বয়সে খানকির পোলা থাপড়াইয়া তোর দাঁত ফালায় দিমু বেশসা মাগির পোলা হাদিস সম্পর্কে জানিস কি,1,religion
এই।কুততা।বাচচা।দের।সাথে।ইললামের।কথা।বলে।কি।লাভ।এদের।জুতার।বাড়ি।দেয়া।হোক।আগে,1,religion
ভাই দেওয়ান বাগিত আসল বন্ড দেওয়ান মাগির জন্মের টিক নাই,1,religion
কুত্তা ছাড়া কিছু না,1,religion
তোরার মারে চুদি মাগির ফুয়া,1,religion
সালার পুত তুই বুজচ কিবলছে তুই ভনড,1,religion
এই শালা ভন্ড তোর চুল তো পিঠ পরযোন্ত,1,religion
শালা তুই ও তো বাল পাকনা।,1,religion
মাদারচোদদের পাইলে জুতা দিয়ে চুদতাম 😡,1,religion
জনাব আমি ওরে হাতের কছে পাইলে ঘড়ি ধরা মিনিট ছেড়া জুতা দিয়া কসাইয়া মারতাম।আসলে হেতে হুরা হাগল।,1,religion
পুরা মাদার,1,religion
কতবড় বোকাচোদা হলে এগুলা বলে।আর এদের যারা দাওয়াত বা তাদের মাহফিল অনুষ্ঠান এ যায় তারা আরো বড় মাপের বোকাচোদা,1,religion
এই হালা পাগল বন্ডু মাজার পোজারী,1,religion
মুরগি কুত্তার বাচ্চা,1,religion
এই কুত্তার বাচ্চা কে কোথায় পাবো !!?,1,religion
তিন কুত্তা আর এক কুতন্নি অযথা ঘেউ ঘেউ করছে । এদেশের স্বাধীন হয়েছে মূর্তি টাঙ্গানোর জন্য নয় । হিন্দু মুসলীম বৌদ্ধ খৃষ্ঠান এই বাংলায় সবাই স্বাধীন ।,1,religion
কুকুরের বাচ্চা তরে কে উপস্তাপিকা দিছে তুই নিজেই ত একটা নাস্তিক,1,religion
এই শালার পোলা ইহুদীর দালাল তুইত মনে হয় কোরআন পড়তে পারছ না আলেমদের খারাপ ভাবে দেখাস।,1,religion
ও মাগির পুয়া তর মারে কর,1,religion
হাহাহাহাহা এরা মানুস নামের কুকুর কুকুর এর চাইতে বালো সালার বুজলাম না মানুষের বাবা কয়টা হয় ওগো দেখি বাবার ওবাব নাই,1,religion
এইরকম ভি ডি ও বা মডেলিং বা আদর্শ সরুপ স্থাপন করায় বাংলাদেশের সমাজটা ডেমনা ও খানকি মাগীতে ভরে গেছে। লক্ষ লক্ষ কোটি কোটি ডেমনা ও খানকি মাগী রোজ রোজ তৈরি হচ্ছে। ভালো মেয়েদেরকেও এরা সব দিক দিয়ে পাকা খানকিতে তৈরি করে। আমার ভুরিভুরি অভিজ্ঞতা আছে। আমি অনেক অনেক দেখেছি । আমাকে ভুগিয়ে ভুগিয়ে তছনছ করে বরবাদ করে দিয়েছে এক খানকি মাগী। এরা নিজেরা হাজার জনকে দিয়ে চুদিয়ে বেড়াবে গুদের গর্ত কুঁয়োর মতো বানাবে সেই কুঁয়োতে ভাতারকে ডুবিয়ে ডুবিয়ে মারবে শালি খানকির জাত। তারা হাজার ভাতার করে বেড়াবে অন্যের বাচ্চার জন্ম দিয়ে ভাতারকে দিয়ে বড়ো করাবে। প্রবাসি ছেলেরা কত কষ্ট করে জীবনের ঝুঁকি নিয়ে দুটো টাকা রোজগার করে বাচ্চা মানুষ করে তাও আবার অন্য লোকের বাচ্চাকে? এ সমস্ত ভুক্তভুগি ছেলেরা ছোটখাটো একটু কিছু করলে দুনিয়াতে আগুন লেগে যায়। আর মাগীদের বেলায় কেউ কিছু বলবে না। ডেমনা ও মাগীরা এ সমস্ত মাগীদেরই দালালি   করে। কোন সময়ে ভাল ছেলেরাও এই মাগীদের দালালি করে। ভাল ছেলেদের কবে চোখ খুলবে কে জানে ???????,1,religion
তোর বউয়ের ভোদ চোদ জাইয়া,1,religion
সালা মাযার পুযারি,1,religion
ভন্ড তাহেরি মাজার পূজারী মাদারচোদ,1,religion
হুজুর সত্যি কথা বলেছেন ঐ সালা গাজাখুর,1,religion
তুই কুত্তার মুখে মাওলানা শফী সাহেবের নাম মানায় না।,1,religion
ওর ফাঁসি হওয়া উচিত যদি ফাঁসি হয় তা হল ওর কোন ক্ষমা নেই ও একটা কুকুরের বাচ্চা,1,religion
আরো ভিডিও বানান ভাই শালারা বন্ড,1,religion
শালা কুকুর টা,1,religion
এই শুয়োরের বাচ্চা তোর ছয় মিনিটের ভিডিও তে পাচ মিনিট তোর ঘেউ ঘেউ সুনতে হয় কেন,1,religion
টিক টক ষারা করে এরা হারামজাদা,1,religion
সালারা টা এক সাথে।এখানে টা কুকুর আর জন মানুষ। আর আল্লাহর বান্দা জন এই যতেষ্ট,1,religion
জুতাদি পিঠাই শালারে,1,religion
মহিলা টাকে মাগি মাগি লাগে,1,religion
কিরে ঝাওরা মাগির পোলা তোর বউ তো মালটা কঠিন। ঘন্টা চোদলে কতো টাকা।,1,religion
এই ভন্ড হুজুরকে ধরে জুতা পেটা করা হউক শালা ইহুদী ক্রিস্টানের দালাল,1,religion
কুততার বাচ্চা,1,religion
জাইরা সালা তুই,1,religion
ওতো একটা মাদার চোদ।ওকে আর কোন মাহফিলে যেনো দেখা না যায়। তাহলে ওকে জুতা মারা হবে।,1,religion
কুত্তার বাচ্চা নাস্তিক,1,religion
শালা বাল পাকনা,1,religion
সালারা শয়তান,1,religion
দেখা যায় তো তোরে বান্দর এর মতো হালা কুত্তা,1,religion
আযাহারি মাগির পুলারে জুতা পিটা করা হক। কার আল্লার নবীকে কী আযাহারি মাগির পুলায় দেখেছিলো কখনো না কী। আল্লার নবীর ছবি আছে ওর কাছে। না কী কুরআন শরিফে কোথায় লেখা আছে যে নবীর গঠন হিসাবে। আযাহারি তো আসলেই কাফের।,1,religion
কুত্তার বাচ্চা নাস্তিকের বাচ্চা নাস্তিক তুদের জুতা পিঠা কর দরকার,1,religion
তুই জানুয়ার দেয়ানবাগী ভাল হবি না। তুই বাতিল ওরা হক।,1,religion
তোর মা তোরে কোত্তা দিয়া চুূদাদিয়া তোরে জন্মদিয়েছে,1,religion
কুত্তাদের ফাসি চাই,1,religion
ভাই এরা মাওলানা না এরা হচ্ছে শুয়োরের বাচ্চা আমাদের মুসলিম ধর্মে যেমন শূকরের নাম্বার হারাম ঘুষ খাওয়া হারাম তাই ওদের সাথে তুলনা করলাম কারণ দুনিয়ায় অনেক কুকুর আছে কুকুর একটা মান সম্মান আছে শুয়োরের বাচ্চা শুয়োরের বাচ্চা এ সম্বন্ধে কি জানবে হাজী সম্বন্ধে কি জানো তুই তো লেখাপড়া করিস নাই শুধু মাগির দুধ দয়া করে কেউ হাজী সম্পর্কে মন্তব্য করবেন না এদের সাথে হাজির তুলনা হয়না আর লাখো লাখো হাজী মাথা ন্যাড়া করে নে এটা ফরজ কিনা নফল কি আমি জানিনা এই শুয়োরের বাচ্চার ঘন দুলা দিন,1,religion
দেওয়ানবাগীর হোগামারা সারা,1,religion
দোদের দলটাই পুরা সয়তান সালারা,1,religion
ঐ কুওার বাচ্চা ভন্ড কে টেইজে বসতে দিছে কেন। ওরে জুতা দিয়ে পিটে বিদায় করার দরকার ছিল। হে ভন্ড বাচ্চা শুন আমার বাড়ি সিলেট হুজুর যা বলছে টিক ই বলছেন সিমাহিন জগংন্য কাজ হয় ঐ মাজারে গাজা কায় মদ কায় কবরে সেজদা করে আর কত কি,1,religion
? ।। শালায় গাঞ্জা খইয়া লইছিলো😹😹,1,religion
কুক্কুর ওর বাচ্চাকে জুতা পিটা করা উচিত,1,religion
ছাগলের তিন নাম্বর বাচ্চা সালা বিদাতী ভন্ড,1,religion
তুই একটা কোত্তার বাচ্চা বড্ড,1,religion
সেবকটা মাদার চোদ,1,religion
ওরে মাগি রে তোরে হেদায়েদ দিতে হবে না তোর বাসা কই বল আমি তোরে ভালো করে হেদায়েদ দিতাছি,1,religion
ভাই দেওয়ান পুটকা বাগীকে যে মানার সে আল্লাহর চাইতে বেসি মানে আর যে মানে না সে দিনের পরে যে পুটকির চিপার বাল ফেলেনা ঐবাল দিয়েও মানেনা ।আমি মনে করি আপনার ফলোয়ার দের মাঝে এমন পাবলিক নেই যে কিনা এই পুটকার মুরিদ । এই সব মানুষ রুপি ইবলিশ তাড়াতে দেশের পরিচালনা করে এমন প্রধান লুকের দরকার ।,1,religion
আবে কুত্তার বাচ্চা।।।।।দেওয়ান বাগির নামে এত খারাপ কথা বলস কেন।।।।।তুই যাইয়া দেখছস।।।।কি সে কি রকম,1,religion
যারা হুজুরদের নিয়া টিকটক বানায় এগুলো সব কুওার বাচ্চা,1,religion
হাই ওয়ান বাচ্চা দেওয়ান বাগি এতো খেয়ে খেয়ে শুকুরের বাচ্চারা মত হয়ছে,1,religion
এই সব খানগির ভাই ভন্ড কে গুলি করে মেরে শান্তি হয় না,1,religion
ওর মারে চোদে,1,religion
তুই যত ই ভালো হোস।আমরা তকে কখনো ও ক্ষমা করব না।মাগি😡😡😡,1,religion
মাদ্রাসা গিয়েছিস কি কখনো ভন্ড নাস্তিক মদখোর মাজার পূজারি নাস্তিক কোথাকার লাথি মারতে ইচ্ছে করে তোদের মতো নাস্তিকদের। তুই নাকি এলেম রাসূল সল্লাল্লাহু আলাইহি ওয়াসাল্লাম এর চেয়ে বরো বলো ভন্ড নাস্তিক তোদের লেংটা বাবা এই বাবা সেই বাবা।,1,religion
ত্রই সয়তানের বাচ্চা তুই কাফের কুত্তার বাচ্চা তুই তাবলিগ নিয়া কথা বলছোস,1,religion
শালা মাদারি পীর কাবা হয়।শালা আবাল,1,religion
তাবলীগ। বাক। শালা তাহেরীকে নিয়ে কথা বলছ,1,religion
পুলাপান দিয়ে ওয়াজ পড়ানোর নামের মানুষ দেখানো সালা আবাল,1,religion
হুজুর ওয়াজ করতে আসে না ঝগড়া বাজেতে আসে।।।। মাদার চুদ!!!!! মিজানূর রহমান এর ওয়াজ শুনবি।।।। কিছু শিখতে পারবি,1,religion
এরা মাদার চোদ,1,religion
শালা তুই একটা শয়তান এবং তোর দল ও শয়তান,1,religion
দেওয়া শালার হলো জারজ সন্তান,1,religion
মাগি তোর মুখে প্রসাব করি,1,religion
একজন বেশ্যার পক্ষে এ ধরণের কথা বলাই স্বাভাবিক। ও তো একটা পেশাদার বেশ্যা।,1,religion
এরা হলো নাস্তিক বেজন্মা তারা নিজে খোজ নিয়ে দেখেন আপনার জন্মের সময় টা আর জন্মের আগের টা,1,religion
জুতামার শালারে,1,religion
শুধু গজা না আরো কিছু খাইছে হালারা ভন্ড,1,religion
এই খানকির বাচ্চা মানুষ না অমানুষ ওর বাবা মা ওই খানকির বাচ্চারে শিক্ষা দেই নাই,1,religion
কুত্তার বাচ্চাকে পেলে জবাই করব।,1,religion
এই মাগির পোলা সাহস থাকলে সাতকানিয়া উপজেলায় আই জিলাপি বানায় দিয়ম মাগির পোলা তোর চোদ্দ গোষ্ঠী মারে ছুদি,1,religion
নাস্তিকের গালে গালে জুতা মারো তালে তালে,1,religion
আমি ভারত থেকে বলছি যদি আমি মাহফিলে উপহ্স্তিত থাকলে শালার মাথা ফাটাইতাম,1,religion
ভণ্ড সালা,1,religion
লোপা হইল খানকি ওরে পাটা দিয়া গাভিন করা হোক,1,religion
পাগল ছাগল গরু মগা তাহেরি,1,religion
কুত্তার বাচ্চারা তোরা মুসলমান জাতির কলঙ্ক তোর টুপি খুল দারি চাছ জানোয়ারের বাচ্চারা হারামির বাচ্চারা তোদের জন্মের ঠিক নাই তোকে জনগনের হাতে তুলে দেওয়া হক মাটির নিচে পুতে পাথর নিখেপ করা দরকার তোদের জনে দুনিয়াতে এত গজব হয়,1,religion
এই নাস্তিক বাচ্চাদের পেলে কি করতাম বুঝাতে পারবোনা।বাইনচোদের বাচ্চা তোদেরকে এই দেশ থেকে পেটে পেটে বাহির করতে হবে,1,religion
ভন্ড দেরকে পাছা বেড়াই লাথি মারা উচিত,1,religion
আর এক সুন্নি মাদারচুদ ভন্ডার বাচ্চা,1,religion
শুয়ারের বাচ্চাদের কথা শুনে মনে হচ্ছে ওদেরকে সামনে পেলে ইচ্ছা মতো মারতাম।,1,religion
নাস্তিক চার জানোয়ার এক বাঘ,1,religion
দেওয়ান বাগী ঠাডাই একটা চর মারতে মনে চাইতে আছে।!।চোদনায় খাইয়া খাইয়া পেটারে একচা ডেরাম বানাইছে।।।। দেয়ান বাগী চোদনা পেট পাচাইয়া লাথি মারতে হয়,1,religion
এ ইটা সরকারে দোস এই খানকি মাগি কোনো একসান নেই না। এই সরকারে দেওনবাগি ও মুরিদেরা চোদে,1,religion
মিডিয়ায় ইসলাম নষ্ট করবে হইছে একটা শালাা লিখছে একটা,1,religion
মিনিট শুনলাম ওয়াজ কাকে বলে কিছুই পাইলাম না পাইলাম শুধুই তাহেরীর বদনাম গাওয়া শালা বাল পাকনা শিশু থাপরাইতে থাপরাইতে তর দাত ফেলে হারাম জাদা !,1,religion
এই শালা ত পেন্ট এ মুতার বয়স অরে মিম্বর এ বসাইছে কুন মাদারচুদ,1,religion
তুই তো শালা কুত্তার বাচ্,1,religion
এই হারামজাদা তর ওয়াজ শুনাতো নাজায়েছ,1,religion
মাদারচোদ । গালি না দিয়ে পারলাম না।মাফ করবেন ।,1,religion
সালা ভন্ড তাই ভন্টদের পককে,1,religion
পিটাছ না ক্যা শালা মাজার পূজারী কে,1,religion
চার নাস্তিক কুত্তার বাচ্চাদেরকে জুতা পেটা করতাম সামনে পেলে।,1,religion
জুতা মার সালা সিন্নি খোর কে।,1,religion
বয়ান করার জগ্গতা না নিয়ে চেয়ারে বোসলে আর কি বয়ান করবে?শালা বাটপার,1,religion
এই শালার টুপি কই,1,religion
মাদারচুদ তর বয়স কত নাক টিপলে দুধ বের হবে বাল পাকনা আইছে ওয়াজ করতে এগুলা অই শিশু দোষ না দোষ হলো তার বাবা মা,1,religion
ভাই ওদের কে জুতাদিয়ে বাইড়ান শালা ভন্ড দেয়ান বাগি,1,religion
চোদানির পুতেদেরকে আর ঐ চোতমারানী কে জুতা দিয়ে পিটানের দরকার ছিলো হুজুরকে কোন কথা বলতেই দেইনা,1,religion
এই বাস্টার্ড কুলাংগার বেশ্যার পুত তোর জনমো কুকুরের বির্য দিয়ে।,1,religion
সালা তুই যে কত বড় বাটপার তোর ওয়াজ শুনলে বুঝা যায়,1,religion
মাদারচুদ হুজুর তর মাকে চুচি,1,religion
আমিন সালা ভন্ড বসেন বসেন বসে জান,1,religion
হারামজাদা ছি??,1,religion
হারামি,1,religion
তোর মুখের উপরে আমি পেশাপ করবো তোর পাচার মধ্যে দিয়ে আমি গরম রড ঢুকাবো কুত্তার বাচ্চা গিয়াস,1,religion
ভাই আপনারা বড় শয়তান। আপনারা দেওয়ানবাগী হুজুরের নামে এত ভিডিও করতেছেন আপনারাই তো ভন্ড অন্য জন কে ভন্ড বলেন কেন।। আপনারদের কি মাথা ঠিক আছে। এসব ভন্ডামি করে আপনারা কিছুই করতে পারবেন না।।,1,religion
কুত্তার বাচ্চারা এরা ফাঁসি চাই ভন্ড বাচ্চা ছেলে কুকুর টাকা খাই,1,religion
কুত্তার বাচ্চা দেওয়ান বাগীকে গুলি করে মারলে কোন পাপ হবে না।,1,religion
দেওয়ান বাগি হালা মরছেনি না বাইচ্চা আছে,1,religion
কিরে গ্রেট মাদার চুদ তুই কি আলেম নাকি জালেম তৃই যে অন্য মানুষের নামে গিবত করছ তুই কি বক্তা নাকি তক্তা মাদার চুদ তুই যে বলছিস আমি কারো সমন্দে কথা বলি না তৃই তর বাপেরবেটা নামে বদনাম করিছ কেন গ্রেটার মাদার চুদ তুই একটা বন্ড বাচ্চা সালির পুত তুই অন্য মানুষকে বন্ড বলিস তুই একটা বন্ড তই যার নাম ধরে বন্ড এবং বাটপার। বলছিস তার সামনে যাইলে কথা বলবি ধুনারি কথা ডরে কাপর নষ্ট কইরা লাইবি মাদার চুদ তর সাহষ তো কতনা গ্রেট মাদার চুদ যদি এক বাপেরবেটা সন্তান হয়ে থাকিস। তাহলে তাহেরির সামনে গিয়ে বলিস বন্ড সালা ফোডানির বাচ্ছা কইরাতনির বাচ্ছা,1,religion
দুর লা শালা,1,religion
প্রথম মনে করেছিলাম তুই ভন্ড এখন দেখি তুই ভন্ডর ফেক্টরি😄😃,1,religion
তোর ওখানে শাহ বললেও ভুল হবে গরম হল দিতে হবে খানকিমাগী,1,religion
তুই মদ খাইচছ সালা তুই দালাল তুই খারাপের চোদা।নয়তো আলেমদের পিছনে কেন লাগচছ।তোর কি সেই যোগ্যতা আছেরে ভুল ধরার।তোরচেয়ে বড় বড় জানলে ওয়ালা লোক সেখানে তার ওয়াজ শোনে।তুই তোর মার সোনার মাঝে ছেপ দিয়া চোদ।।এই কথাটা বলতে আমারো খারাপ। গাগছে।বাট কিছুই করার নাই।এরচে খারাপ কিছু থাকলে সেটাই বলতাম,1,religion
ভাইয়া এই কুকুর কি বলল তা নিজের মুখে উচ্চারণ কইরেন না।খুব খারাপ লাগে।ও যে মিথ্যা বলে তা আপনার ফলোয়াররা জানে। তাই এভাবে বলে বলে দেখানোর দরকার ছিলো না।নাউজুবিল্লাহ আর কানে এই অত্যাচার সহ্য করতে পারলাম না।🙉🙈,1,religion
চারটা কুত্তা একসাথে ঘেঊ ঘেউ করছে আর একজন মানুষ শাইখ মামুনুল হক তাদের কে কন্ট্রোল করার চেষ্ট করছে,1,religion
এই কুত্তার বাচ্চাকে যেখানে আছে সেখানেই খতম করে দাও ।শালির মুখে পেশাব কোরে দাও ।ভিকারির বাচ্চা শালা ।টাকার লোভে মাদরচোদ এই শব কোরছে ।,1,religion
বান চুদ,1,religion
এই অমানুষের বাচ্চারে পুঠকি দিয়া গুলি কেন করা হয় না😡😡,1,religion
এই কুত্তারা কোথা থেকে এসেশে,1,religion
শালার মাথা খারাপ হয়েছে,1,religion
কুকুরের বাচ্চার জন্ম কোন জেলার,1,religion
পৃথিবীর নাম্বার ভন্ড তাহেরী কুত্তা,1,religion
শালাগো ধইরা জুতাপেটা করা হোক এবং টেস্টি কি ভিতরে তো গলায় ফাসি দাও শালারা মুসলমান কে অপমান করে তোমাকে অপমান করার শাস্তি সম্পর্কিত ইনশাল্লাহ আল্লাহ শাস্তি হবে,1,religion
বাংলাদেশে এরকম কুলাঙ্গার দেওয়ান ভাগী কি ভাবে চলা ফেরা করে তাকে ফাঁসি দেয়া ফরজ,1,religion
হে আল্লাহ এদেরকে দুনিয়া থেকে নিয়ে যাও নাস্তিকের বাচ্চা দেরকে কুত্তার বাচ্চা,1,religion
এই খানকির পোলাদের কারনে আজ ইসলামের বদনাম হয়তেছে,1,religion
শালি বেস্যা,1,religion
আমার মনে হয় বেজন্মার বাচ্চা। তুইত,1,religion
মন থেকে বলছি আমি ওখানে থাকলে ঐ কুত্তার বাচ্চা গো মাইরা নিজেও মৃত্যুর জন্য তৈরি হয়ে যেতাম,1,religion
সালা বেয়াদব,1,religion
ভাই আপনি বাংলাদেশ এ আসেন অমরা এক সাথে সালারে বাঁশ দেই,1,religion
মিজানুর রহমান আজহারি হুজুরকে যে কুওার বাচ্চা বন্ড কাফের বলে সে হল আস্ত একটা কুওার বাচ্চা একটা অমানুষের বাচ্চা।,1,religion
এই খানকির পোলারে শুক্রবার জুমার নামাজের পর বায়তুল মোকাররমের সামনে জুতাপেটা করে তারপরে একে ফাঁসিতে ঝুলানো উচিত 💯🤙✋,1,religion
পুলা ত নয় সে আমার সুনা খা তাহেরি,1,religion
হালারে ফাসি দেওয়া তরকার,1,religion
মাগির পুলারা অলী নিয়ে কথা বলছ,1,religion
আমার হালা,1,religion
দেওয়ান বাগি কুত্তার বাচ্ছারে জবাই দেওয়া উচিৎ,1,religion
ওরে হিজরা দ্বারা চুদে দিলে ভালো হবে 😁😁 শালা বাইনচুদ 😠😠,1,religion
কুত্তার বাচ্চারে গু খাওয়া,1,religion
কুত্তার বাচ্চারা,1,religion
হালা চোর,1,religion
এরা সবাই জারোজ,1,religion
এই শালাকে জুতা দিয়ে পিডানো উচিত,1,religion
এই শয়তানের মাহফিলে লক্ষ্য লক্ষ্য মানুষ দেখতে পেলাম তারা আসলে মানুষ না সব গরু ছাগল। আমার নিজেস্য গবেষণাগারে গবেষনা করে দেখলাম বাংলাদেশে মানুষের চেয়ে গরু ছাগলের সংখা অনেক বেশী। আমরা সবাই জান জ্ঞানহীন মানুষ পশুর সমান।কুরআান হাদিসে সবকিছু স্পষ্ট করে বলে দেয়ার পরেও যারা জ্ঞান অর্জন করতে পারে নাই তারা গরু ছাগলই।,1,religion
এইকুত্তার বাচ্চাদের জুতা মরা দরকার,1,religion
এই কুত্তার বাচ্চাদেরকে গনধুলাই দিয়ে কাপড় খলে সারা বাংলাদেশে চক্কর দিয়ে ফাসিতে ঝুলালে আমার মনটা একটু সান্তি হোত। কুত্তার বাচ্চা দেওয়ান বাগি😡🐕👟👞জুতাদিয়ে মার হারামজাদাদেরকে,1,religion
গোলাম জিলানী তোদের মতো কুকুরের বাচ্চার কারণে আজকে মানুষ গুলো খারাপ হয়ে গেছে কোরানের কথা বলে না একজন আরেক জনের বিরুদ্ধে কথা বলে ৷৷। এইসব ভন্ড পীর মাজার পূজা সম্পর্কে আর কিছু বলার নাই আমার ৷৷।।।। আপনারা সবাই কিছু বলেন 👎👎👎👎,1,religion
শালা তুই তোর মাকে বিয়ে করতে পারবিরে শালা,1,religion
সালা হাইওয়ানের বাচ্চা,1,religion
এই বাইন চোদ তোর বাড়ি কয় তোর মত চেটেরবাল কিবুঝবি তোর জন্মের ঠিকআছেকিনা তোর মারেজিগ্গাসা কর।,1,religion
ঐ জানুয়ার কুন মাজারে গাজা খায় না দেখাবি,1,religion
তুই যে বলচিস হাফিজুর রহমান ভন্ড। আরে বেটা তোর সাহস থাকলে তুই সামনে আইসা বল বেটা।তুই কুলাঙ্গার। তুই মুনাফিক,1,religion
ভন্ড হারামি,1,religion
কুত্তার বাচ্চা ভন্ড ইহুদি বললে ও পাপ হবে,1,religion
মাদারচোদের পাছা মারার সু ব্যাবস্থা করা হোক,1,religion
জানোয়ারের বাচ্চা এটা এদের কেউ মারে নানি এসব সব বেক্তিগত চ্যানেল,1,religion
শালার বাচচা ভন্ড দেওয়ানবাগি। এরা কেমন মানুষরে৷ বাংলাদেশ এদের বিচার হয়না কেনো।।। এদের দেশ থেকে বাহির করে দেওক।। আল্লাহ এদের হেদায়েত দান করুন আমিন,1,religion
সব শালা কুত্তার বাচ্চা এদের ফাঁসি দেওয়া উচিত তোমাদের বাংলাদেশে কোনো বিচার হয়না আমার বাড়ি বাংলাদেশ হলে দেখতাম সব শালা কে কুত্তার বাচ্চা,1,religion
তাহেরি কুত্তার বাচ্চা কি জুতা দিয়ে পিটা নো দরকার,1,religion
শালা মনে হয় মাল খাইছে,1,religion
ওই। কুত্তার বাচ্চা যে মারা গেছে সে আসলো কি করে মোটা চোদা,1,religion
ভাই এই শয়তান টা দজ্জালের দালাল। আরে ও তো একটা নাস্তিকের বাচ্চা নাস্তিক। সে যদি নাস্তিক নাই হয় তবে কেন কোরান হাদিস সম্পর্কে এই ভুল কথাগুলো বলল। আরে সে যে কত বড় ডাকাত সেটা বাংলাদেশের জনগণের বুঝার কোনো বাকি নেই। সে প্রকাশ্যে এত বড় ভন্ডামি কথাগুলো বলছে তাও আবার কোরআন হাদিস সম্পর্কে। শয়তানটা মারা গেছে না এবার বুঝবে। ঠেলা,1,religion
এইখানে কোন কুত্তার বাচ্চা জারজ সন্তানগুলো আনলাইক দিছে?,1,religion
তরে জুতা দা বাইরাইয়া গাল ফাটাইয়া লামু কুলাংগারের বাচ্চা।তুই কিসের বালের বক্তা কুত্তার বাচ্চা তুই কিয়ামতের আলামত,1,religion
এই হালার ইমানী চিকিৎসা দেওয়া দরকার,1,religion
দেওয়ানবাগী কুকুর বাচ্চারে সামনে পাইলে জুতা দিয়া তিন টা বারি মাতাম,1,religion
সালা মাদার চােদ ভাল পাকনা তাহেরির জুতা মুছার যােগতা তর নাই,1,religion
যারা ডিসলাইক দিছে এরা প্রত্যেক্টা জারজ বাচ্চা জারজ হুজুর হল বাঘের বাচ্চা গজন সব চুপ,1,religion
এসব পাগলাচোদাদের পুটকির মদ্ধে শালকাঠ ডুকাইতে মন চায়। দেওয়ানবাগীরে কুত্তা দিয়া চুূদাও। বাংগালী এখনো এতো মুর্খ যে ওর পা চাটে মুর্খ বাংগালি এজন্যই উন্নতি নাই সালা গরিব মুর্খ বাংগালী আল্লাহর কাজ না করে উল্টো দেওয়ানবাগি চুদাও।,1,religion
মাদার চোদের বাচ্ছা,1,religion
তিন মাদারছুদ আর এক বেসশা মাগির সাথে একজন আলেমের টকশো ওই নাস্তিকরা তো জানে না একজন আলেমের সাথে কি কথা বলতে হয়।,1,religion
এরাত হারামির ছাওয়াল,1,religion
সালা এক টা বড় ভন্ড,1,religion
এসব মাগির পোলা গুলা ওয়াজ করতে যাই মানুষের শেকায়েত করে এবং মানুষে মানুষে দাঙ্গা বাজায়,1,religion
হালারে পাইলে জুতা পিটা করতাম,1,religion
এই হালার পো তুই তো নিজেই ভনডো,1,religion
সালা ভন্ড তরে যে মারে নাই তর কপাল আমি সামনে পেলে জুতা দিয়া পিটাইতাম মাজার পুজারি ভন্ড কুততা,1,religion
দেওয়ানভাগী হচ্ছে কাফের । জানোয়ারের বাচ্চা । শয়তানের বাচ্চা । ফেরাউনের বংশধর।,1,religion
তুই ত লুচ্চা,1,religion
সরকার ভালো ভালো আলেমদের শাস্তি দিচ্ছে।এই কুওা রে ফাসিঁ দিচ্ছে না কেন?,1,religion
কুত্তার বাচ্চারা ইসলাম ধ্বংস করছে,1,religion
সালি তর মারে চুদি,1,religion
এই ভন্ডরে কোন জানোয়ারের সাথে তোলনা করি বেভে পাইনা,1,religion
ভাইয়ারা কুত্তার বাচ্চা বলে গালি দিয়েন না আমার দেশের কুত্তারা অসম্মান করা হবে অদ্ভুত একটা করে খাব মাদারচোদ ভন্ড ভন্ড দেওয়ানবাগী,1,religion
দেওয়ান বাগি কুকুরের বাচ্চা,1,religion
বিউয়ারছ বাড়ানোর জন্য কি করছো মাগির পুলা,1,religion
এটা মুসলমানের দেশ। এখানে মাদারচুদের কোনো জায়গা নেই।,1,religion
অবশ্যই এই শালী নংবেশশা,1,religion
ওরে কুত্তার বাচ্চা তুই মা ফাতামার এক নগের সমান হবি না ?ওরে ভন্ড তুকে যদি পাইতাম তাহলে কাঁচা মুরগী ডুকিয়ে দিতাম,1,religion
তার মারে চূদি তোর বাপেরে চুদী তোর বইনেরে চুদি চুদি চুদি তোর মারে চূদি,1,religion
অই মাদারচুদ মেডিয়া কি লেখলি মাদারচুদ মুরখর দল পোস্ট ডিলিট কর,1,religion
সালের ভন্ডরে সব জঙ্গির দল মারামারি ছাড়ে কিছু নাই,1,religion
চিস্টি ওয়াজ চ্যানেলটা যারা চালায় ঐ শালারাই তো ভন্ড কি ডাল দেয় একটা আর বক্তব্য দেয় আরেকটা,1,religion
দুই বছরের পোলাও পেল পাকনা হইয়ে গেছে গিবত ঘাওয়া শুরু করছে মাদার সোধ,1,religion
খানকির মাগির বুদায় বাশ দিয়ে দারনো উচিত,1,religion
ওদেরকে চেনার উপায় একটাই তোর মতো ভণ্ড খানকির পোলা ওয়াজ করতে পারো স্টেপলার আজকে শালার ঘরের শালা খানকির পোলা মাদারচোদ,1,religion
শালি জারজ সন্তান। নাস্তিকের বাচ্চা 😡😡😠😠,1,religion
শাহরিয়ার কবির একটা শুয়োরের বাচ্চা,1,religion
শালা তোর কপালে জুতার বারি,1,religion
যে এই ভিডিও টি বানাইছে ও আসলে একটা জানোয়ারে বাচ্চা,1,religion
সালাকে জুতা পিটা করা হোক। এবং ফাঁশি দেওয়া উচিৎ,1,religion
মানুষের মাথায় বুদ্ধি থাকে আর ঐ দেওয়ানবাগীর পেটে বুদ্ধি থাকে👿👿👿👿শয়তান শালা,1,religion
তাহেরি ভাল কি খারাপ জানি না তাহেরি কি তর বড় না ছেেোট? খানকির পলা নাম্বার এর বিয়াদপ ওরে আদপ কায়দা শিখা শালা বিয়াদপ বক্তা অল্প বয়সে পাকিলে বাল দুঃখ তার চিরকাল ওয়াজ কাকে বলে কিছুই পাইলাম না পাইলাম শুধুই তাহেরীর বদনাম গাওয়া শালা বাল পাকনা শিশু থাপরাইতে থাপরাইতে তর দাত ফেলে হারাম পস্রাব এর গন্ধ ও যায়নি ওয়াজ এ নেমে গেছে। কিয়ামত আর বেশি দুর না দেখে মনে হচ্ছে এখনো ও শেষ করেনাই আর কিছু আবাল বলতেছে তারা শিশু বক্তা ছি ছি এই গুলোর মধ্যে থেকে ইসলামের কি শিখতে পারবে? আবার নিজেকে হুজুর বলে দাবী করতেছে তুই বক্তা না তক্তা পরের গিবত বলিস অন্যের গিবত বলা হারাম তুই জানিস না,1,religion
টকশো চুদাও??? এক পক্ষে জন অন্ন পক্ষে জন।,1,religion
ওরে পাগলের দল এইটা গান নারে শান গাইতেছে,1,religion
দেওয়ান হালার যারা মুরিদ আছে তারা সবাই হচ্ছে দেওয়ানের পা চাটা কুত্তা,1,religion
কিছু বলার ভাষা হারিয়ে ফেলেছি ভাই এই গুলো কি শুরু করেছে এই কুত্তার বাচ্চা গুলো এইসমস্ত জানোরদের কেনো জবাই করা হচ্ছেনা কেনো আপনার এই ভিডিওটা আমি নিজের চ্যানেল এ পোষ্ট করবো ভাই রিপোর্ট করবেন না প্লিজ এই সমস্ত কুত্তার বাচ্চাদের মুখস খুলে দিতে চাই,1,religion
এত বড় কেনো ভাই বাবীর দুধটা,1,religion
এই কুত্তারে আমি কাছে পেলে মেরে ফেলতাম।,1,religion
পিটানো দরকার শালাগো,1,religion
কুত্তার বাচ্চারা মামুনুল হক সাহেবকে কথাই বলতে দিচ্ছেনা,1,religion
এ কুত্তার বাচ্চাকে বিনা গোসলে কুকুরের মতো পুতে রাখতে হবে তাহলে আমরা মুসলমান শান্তি পাবো,1,religion
শালা তুই জারজ,1,religion
লোপা খানকীর বাচ্চার বুদা ছিরা কুকুর দিয়ে খাওয়ান,1,religion
নাস্তিকের বাচ্ছাদের কে কঠুর শাস্তি দেওয়া দরকার,1,religion
তুই একটা কুতার বাচ্চা সব তের বাবা তায়েনা কি,1,religion
এক আবালের বাচ্চা তাহেরের নামে গীবত করিতেছে আর সামনে বসা বড় আবাল গুলা বলিতেছে ঠিক আবালের বাচ্চা আবাল,1,religion
ডিসলাইক দেওয়া হারামির বাচ্চাগুলা দেওয়ানবাগির মুরিদ।,1,religion
তাহেরির গা ভরে কুত্তা দিয়ে মুতানো লাগবে,1,religion
ডিজলাইক দিচ্ছে কোন মাদারচোদ গুলা?,1,religion
কুত্তার বাচ্চা নেসা করে এই সব কথা বোলেচে,1,religion
? এইবার ডায়রেক হালার অশিক্ষিত আচোদারা ডাইরেক্ট বানান লেখতে পারোনা কিন্ত ইউটিউবার হইতে চাও,1,religion
আমাদের প্রধান মন্ত্রীর উচিৎ উনাকে পাছায় লাত্থি মেরে ইসরায়েল পাঠানো। ইহুদিদের চাইতেও খারাপ লোক।,1,religion
অন্যের গিবত করে আর মুখে কোরানের নাম উচ্চারণ করে। ভন্ড শালা শিশু বক্তা। তোর শ্রোতারাও আর ভন্ড রে শালা। আগে নিজে ঠিক হয়ে যা। কোরান হাদিস থেকে কথা বল যাহাতে মানুষ কিছু জানতে পারে বা শিখতে পারে। তোর ওয়াজ শোনে ত মানুষ পরনিন্দায় শিখবে।,1,religion
এই শালার বাচ্চা সমতুল্য ওয়াশ করতে সিনিয়র কে সম্মান দিতে নিজেকে কি ভাবো দেখে তো মনে হয় যে তুই ওয়ান টুতে পরশ তোরে আল্লায় সর্দি সেকন্ড দিছে কিন্তু তুই তার অপব্যবহার করছ অল্প বয়সে পাকা বেশ ভালো না ইডিয়ট,1,religion
তুই কুত্তার হদাইস বন্ড়ামি চার তুই কাদিয়ানির পোলা তোর কথা কাদিয়ানির মত তোরেজোদি পাই জুতাদি পিটমু,1,religion
বোকাচুদা দেওয়ান বাগী শালার বিচিতে লাথি মারা উচিত,1,religion
দেওয়ানবাগীর ছাগু গুলোরই কাজ 🤔🤔🤔🤔,1,religion
খানকির পোলা আজাইরা তোর আজাইরা ভিডিও গুলো ভালো লাগেনা ছাগলের তিন নাম্বার বাচ্চার মতো লাফাস🤣🤣,1,religion
কে এই সালাদের কে মাহফিলএ আনে যারা আনে তারা ও সালা ভন্ড,1,religion
ভন্ড দেওয়ান বাগী।,1,religion
চেনেলের ভাই এই বানচুদের নাম্বারটা দেন,1,religion
কুকুরেবাচচারচুদাটিকনাই,1,religion
জন্তু জানোয়াররাও আল্লাহ কে সিজদা করে। একে জানোয়ার বলে গালি দিলে জানোয়ারের অবমাননা করা হয়। এর কি শাস্তি হবে তা আল্লাহ ভালো জানেন?,1,religion
এই খানকির পোলা গো মাইরা পুটকির মধ্যে বোম্বাই মরিচ দিয়া তারপর বর্ডার পাস কইরা ইন্ডিয়ায় মালাউন গো কাছে পাঠায় দেওয়া উচিত কারণ কেয়ামতের ময়দানে মালাউন গো আগে এই খানকির পোলারা জাহান্নামে যাবে আর একটা কথা এগুলারে যদি আমি ঢাকায় পাইতাম এগুলারে কুত্তা পিটান পিটাইতাম এই খানকির পোলারা ইসলামের বারোটা বাজাইছে এদের কারণে আজকে মুসলমানরা মার খাচ্ছে,1,religion
এগুলা পাগল,1,religion
শালা একটা ভন্ডা,1,religion
শালার সবগুলো ভন্ড আল্লাহ জানে এদের কি হবে,1,religion
মাথার চুল কাটুকরলে আবুলাহাবের বক্ত হয় তকে কে বলছে তুই যে পাগল বাড়িতে জানেনি শালা হাইওয়ান কুত্তা কামরাইলে ইন্ডিকশন ল শালা পাগল,1,religion
এই শুয়োরের বউ হলো নাস্তিকদের সম্পদ যে যত পারো খাও আসিফের বউয়ের ভিতরে আস্ত গাছ চলে যাবে আর এই খুশিতেই আসিফ গর্ভবতী হয়ে গেছে,1,religion
আরে কুত্তার বাচ্চারা তোরা মুসলমান নামের কলংক ।,1,religion
মাসুদ একটা গুদেরবেটা,1,religion
শালারে জুতা মারেন কুতা,1,religion
এই হোলো গরুর দালাল মুখে আল্লাহ করে পাইজলামি,1,religion
দেওয়ান বাগীর মারে চুদি,1,religion
ছাও 😁ছাগল😊😊😊ছাও পাগল,1,religion
ছাগলের বাচ্চা বেয়াদব কোথাকার ‌ তরে জোতা পিটা দেওয়া হবে,1,religion
বাঁশ দিমু হারামজাদা এই ওয়ার্ডগুলো কি কোন সভ্য মানুষের ভাষা হতে পারে? এই অপদার্থ মোল্লার কাছ থেকে মানুষ কি শিখতে পারবে অসভ্যতা ছাড়া🤔,1,religion
সালি মাগি চুল ছাইড়া হুজুরের সামনে বসছে আবার তর্ক করে সাথে আরো টা ছাগল জে বিষয়ে ঘেন নাই সেই বিষয়ে কথা বলে,1,religion
খানকিমাগী তোর মারে চূদি মাগিমাগি,1,religion
দেওয়ান বাগুরে হোগা মারতে মন চায়,1,religion
এর সবচেয়ে খারাপ গন্ধযুক্ত পাদ দেওয়ানবাগীর মুখে মারা উচিত তাহলে সে ঠিক হবে,1,religion
শালারপুত মাজার পুজারি কে জুতা দিয়ে পিটা,1,religion
মিথ্যাবাদী খারেজির বাচ্চা মুনাফিক,1,religion
আল্লাহ তুমি এই বেয়াদব কুলাঙ্গার কে ধ্বংস করে দাও,1,religion
হে সালা তুর কাজ নাই মনেহই দালাল,1,religion
ফকিন্নির বাচ্চারা তদেরত খবর আছে মরনের সময় বুজবি,1,religion
দেওয়ান বাগী কুকুরের বাচ্চা,1,religion
হারামযাদা কোথায় হাদিস পেলে তুই। তোকে পেলে তোর চাপার দাত গুলো ফেলে দিতাম সালা ভন্ড কথা কার। আর তুই যে বনায় দিলি এটা তুই রে। শয়তান তুই। সালা ভন্ড কথা কার।,1,religion
বেশী বাল পাকনা,1,religion
বান্ধির পুত তরে পাইলে মখের ভিতর ধন খাওয়াইতাম।।।,1,religion
ওহাবীর বাচ্চাদের জুতা পিডা করা দরকার,1,religion
তুমি হারামী টুপি ওয়ালা । তোমার মুখে গু,1,religion
মাগীর পোলা,1,religion
আসল ভন্ডতো আবে হালায়। গাধা নাকি সে।,1,religion
সালা তাহেরির মুখে জুতো মারা দরকার 🐮,1,religion
ভাই শালা একটা পটকা মাছ মানে টেপা মাছ 🐡🐡🐡,1,religion
সব কয়টা নাস্তিক বে জম্মা আর উপস্হাপিকা নাস্তিকদের দালাল???,1,religion
এ দেশের সরকার ভালোনা তানাহলে এই ভন্ড কুত্তা দেওয়ান মাগী এ কথা বলার পরও কিভাবে সে এ দেশে থাকে দেওয়ান মাগী হচ্ছে পতিতালয়ের গলিতে নষ্টা মেয়ের গর্ভে জর্ম নেয়া এক যারজ সন্তান সুধু ও একাই যারজ না অর মা বাবা সবাই যারজ ছিলো তাই সালায় এত ভন্ড,1,religion
ফকিরের বাচ্চা তুমিও বাটপারি শুরু করছো,1,religion
একজন বেগানা উলঙ্গ নারী জাজ!! হবে?? এদের লজ্জা শরম বলতে কিচ্ছু নেই,1,religion
টা আনলাইক হইলো দেওয়ানবাগীর আবালচোদা ভক্তের,1,religion
তদেরকে কুত্তা দিয়া পুটকি মারানো দরকার,1,religion
শালা মিত্যা আমির হামজা তর মারে বাপ কাংকার পুলা,1,religion
মুরগিচুর শাহরিয়া কবির সহ চার জন ছাগল আর মামুনুল হক বাঘ,1,religion
তীরের উদাহরণ দিয়ে ভালো করেছ তোদের মতো ভন্ডরা তীরের মত ইসলাম থেকে বাহির হয়ে গেছোস।। পাগলের বাচ্চা কোথাকার।।,1,religion
তোরে জুতা দিয়ে পিটানো দরকার হারামজাদা হারামজাদা তোর কি মরনের ভয় নেই ধর্ম ব্যবসা করে দুনিয়াতে না চললে তোরা গোমরা হয়েছিস সাধারণ জনগণ রেও গুমরোয় বানাতে চাস হারামির ঘরের হারামি,1,religion
দেওয়ান বাগির মারে চুদ,1,religion
দেওয়ানবাগী হচ্ছে এক্সট্রিম লেভেল এর মাদারচোদ।।,1,religion
ভন্ড বাইনচোদ তারা।,1,religion
তোরে পুটকী মারা দরকার শালা ভন্ড,1,religion
সালারে ফাসি চাই,1,religion
তুই সালা ভন্ড ওরাসটিক,1,religion
এই মাদার চোদ পুরা বয়ান দে এই মাদার চোদ পুরা বয়ান দে,1,religion
দেওয়ানবাগিকে আমি কুকুরের টয়লেট খাওয়াবো।,1,religion
লাল শালা তো গাঁজা খোর তার কথা বলার ধরণ দেখেছেন আমি সিলেটি,1,religion
এগুলু।কি।পাগল।।নাকি।ভন্ড,1,religion
তুই বাল আমার দেওয়ানবাগী তোর জন্ম কি পতিতালয়ে হইছে কুকুরের বাচ্চা,1,religion
তুই হাফিজুর রহমান সিদ্দিকিরে বলস খোদা দাবি করছে তুই সালা দুনিয়ার খারাপ,1,religion
এই বন্ড জানোয়ার কে আর বেঁচে তাকার অধিকার নাই মুসলমান জাগো ওরে বাংলাদেশ থেকে পিটিয়ে বাহির করেন,1,religion
বাইনচুত মাকা বকতা,1,religion
এ শুকরের বাচ্ছা নাস্তিকদের জুতা মার,1,religion
মাদাচোদ তুই বড় ভন্ড,1,religion
তর ওয়াজে যত লোক জাই সবই হল গান্জাখুর সালা ভন্ড,1,religion
দেওয়ানবাগী কোন আবাল 👌,1,religion
একে পীর না বলে শয়তান দেওয়ানবাগী বলতে হবে।এই হারামজাদা কুকুরের চেয়ে জঘন্য।নটি র পোয়া।,1,religion
এই বন্ড দেওয়ান বাগিকে জোতা মাৰা হোক,1,religion
কুরআন হাদীস উচ্চারণ করতে পারিসনা তুই মাযার পুজারী তুই কাফের তোরমুখে গিতাও মানায়না হালার পুত,1,religion
মুর্খচুদা বক্তা ভন্ড,1,religion
সয়তান মুরগি চোরা,1,religion
দেওয়ানবাগী শালারে স্টাম্প এর সাথে বাইন্ধা শোয়েব আখতার আর ব্রেট লি রে দিয়া বিচির মধ্যে কয়েকটা বল করাইতে পারতাম তাহলে মনডা শান্তি পাইতো😀😀,1,religion
তাহেরি মাকে চুদি,1,religion
শালার টাক্কু শালার মৌস তোগো দুইটারে জুতা দিয়া ভাই রান দরকার ইসলাম হলো সবচেয়ে সুন্দর ধর্ম আমাদের ধর্ম তুই হিন্দু বৌদ্ধ খ্রিস্টান এ আবার কি কথা কস বানচোদ তব জব করেন দরকার ইসলাম বিরোধিতা করস শালারা,1,religion
হালা ভন্ড পীর তাহেরি,1,religion
এই ভন্ড দেওয়ানবাগী থাকে কোথায়। এই শালা বাংলাদেশে থাকেন না বিদেশে থাকে বাংলাদেশ থাকলে কি তো হত্যা করা উচিত তাকে। এই দেওয়ানবাগী সালা মা ফাতেমাকে নিয়ে অনেক বেয়াদবি করেছে। এই শালার দেওয়ানবাগীকে ফাঁসি দিয়ে মেরে ফেলা উচিত বাংলাদেশ সরকার দেখেনি না দেখে। এই শালা অনেক বেয়াদবি করছি আর সহ্য করা যায় না। সব মুসলমান এক হয়ে তাকে মেরে ফেলা উচিত।,1,religion
শালার নাস্তিকের বাচ্চাদের জুতা পিঠা করে এই বের করা উচিৎ😨😨😨😨😨😨,1,religion
তর মারে চুদি বেশি বেশি ভিউ তর মার মাংগের ভিতরে ডুকা তর মারে চুদি,1,religion
এক খাানকি আর তিন খানকির পোলা একজন আলেম কে নিয়ে তামাশা করছে আললা তুমি হুজুরের পাশে থাকো,1,religion
তোদে জরমের ঠুকনাই,1,religion
চুদেন চোদেন চোদে জান শালী মাগী,1,religion
বেপসা করার আর জাগা পাস নাই মাগী লোপা,1,religion
চারজন কুত্তা মিলে একজন ইমানদার কে ধরেছে,1,religion
খানকির পুত মাদার চোদ,1,religion
এই হলো খানকি,1,religion
কুত্তাবাগির দুই গালে জুতা মারো তালে তালে👞👟👠👡👢,1,religion
পাগল লোকেরা বাচ্চ কে বকতা হিসাবে শুনে এমন ছেলে মহিলা গরে জন্ম দেই,1,religion
দেওয়ান বাগী ত দেগি দাজ্জাল।,1,religion
এই বোকা চোদা তাহেরি কার অসিলাই চাওয়া যাই না হারামি চাইবি তোর কাজের অছিলাই চা মূর্খর বাচ্ছা মাজারে যদি যাওয়া যাইতো তাহলে নবীর রওজা তে মানুষ সিজদা দিয়ে বসে থাকতো আমির মাজারে মাথা ঢিপাতে থাকতো এদের থেকে তোদের মাজারের লোক বড় হয়ে গেলো তাহেরি তোর গাজা খরি কথা বাংলাদের মানুষও সব মূর্খ হয়ে গেছে মাথাই কিছু নেই ?,1,religion
র‍্যাংক সালার পেছনে দেওয়া উচিৎ,1,religion
এই খানকি মাগি শাহরিয়া অন্য দুইজন এইসব গুলি জারজ মাদারচোদ ওদের গলায় জুতা দিয়ে পাছায় লাথী মারতে মারতে মুখে পশ্রাব করে নর্দমায় ফেলে মারা উচিত।,1,religion
কেয়ামতের ময়দানে তুদের জন্য জুতার মালা রেডি আছে শয়তানের বাচ্চারা। কোন হাদীসে পায়চস রে। সৃষ্টিকর্তা চাইতের গাঁজা খুর বড় হয়ে গেল। টাকার জন্য এত পাগলামি লজ্জা নেই,1,religion
ও মাগি তরে কুকুর দিয়ে জেলা দরকার,1,religion
টা ছাগলের বাচ্চা একটা বাগের বাচ্চা,1,religion
ঐ মাদারচোদ আরবে মিলাদ আছে এবং মিলাদুন নবী উপলক্ষে সরকারি ছুটি আছে,1,religion
পতিতা উপস্তাপিকা 😡,1,religion
মাদারচোদ তোর কি ওয়াজের বয়স হয়চে,1,religion
কুওার বাচছা নসতিক কিপাপ করছ ইমান নিছেগা আললাহ,1,religion
টাকার দালাল হালার পুতহালা,1,religion
শালারে রে মার,1,religion
নাস্তিকের বাচ্চাদেরকে জুতা দিয়ে পিটিয়ে সাইজ করে দেয়া উচিত,1,religion
এডমিন তুই কিন্তু আর জাই হোস মানুষের বাচ্ছা হতে পারিসনা তুই একটা জারজ কুত্তার বাচ্ছা,1,religion
ভাই এই দেওয়ানবাগী কুত্তার বাচ্চা কথা যখন মনে আসে না তখন মুসলমান বইলা দাবি করতেন আমার খুব কষ্ট হয় যেয়ে এ কুত্তার বাচ্চা সেন আমাদের হযরত মুহাম্মদ সাল্লাল্লাহু আলাই সাল্লাম কে নিয়ে কটুক্তি করে তখন গায়ের রক্ত গুলা যে কেমন গরম হয় তা বইলা বুঝাইতে পারবো না ভাই মনে হয় যে গায়ের মাংস গুলো নিজে কামড়াইয়া ছিড়া বালাই যে আমাদের দেশে এমন এক কুত্তার বাচ্চা আছে যে জায়গায় পার্সেন্ট মুসলমান সেই জায়গায় এমন একটা মানুষ বাস করে যাকে থামানোর জন্য কোন বাংলাদেশে কোন লোক নেই,1,religion
সালা ভাব লয়,1,religion
একটা কুকুরের চারটি বাচ্চা একটি কেঢি আর তিনটি কেঢা করে শুধু ঘেউ গেউ,1,religion
এই চ্যালেন টা যে বানায়ছে ঐ সালা খারাপ,1,religion
তাহিরী হুজুরকে জুতার মালা গলা দিয়ে গরু রামু,1,religion
জুতা দিয়া মারা উচিত সালারে,1,religion
জন নাস্তিক কুকুর সালারা।,1,religion
মুরগী মুরগী কবির,1,religion
চার টাই জারজ সন্তান,1,religion
আমি তাহারি ভন্ডের বিচার চাই শালা একটা মিথা বাদি,1,religion
দেওয়ান মাগির গালে হাগু করতে পারলে জীবনটা ধন্য হত,1,religion
পিটা বক্তা সালারে,1,religion
নাস্তিক পীর ভন্ড পীর থেকে হে দেশ বাসী সাবধান।তাদের কে হত্যা করা দরকার।,1,religion
তুই শালা ভন্ড একটা,1,religion
বেটা নাস্তিক তারাতারি পোস্ট ডিলেট কর,1,religion
এই কুত্তার বাচ্চার ঠোঁট শিলাই করা হবে যেন কুত্তার বাচ্চা কথা বলতে না পারে,1,religion
তোদের উপর আল্লাহর গজব পড়বে,1,religion
ওদের মোছগুলো দেখলেই পিঠাইতে মন চায়।।। নাস্তিকের বাচ্চা।।,1,religion
মার সালারে,1,religion
তর মায়ের ভূদায় গিয়ে মন্দির বানা শালা কালা নাস্তিক,1,religion
👠👠👠👠👠👠 সালা আসলে ছাগল,1,religion
জুতা মার ওই কুতার বাছা কে,1,religion
সালা পাগল।একবার বউ বলে আবার মা বলে।,1,religion
এরকম কুত্তার বাচ্চা মোল্লা গুলো যেখানে সেখানে মাজারে গাজা আছে বলে মোল্লাটারে জুতা পেটানো করা উচিত,1,religion
কুওা হালার পুত,1,religion
সালা মার কোব,1,religion
তুমিত নাবালক বকতা গিফত গাউ কেমনে পিটায়া পাছার খাল উটানোর উচিচ সালা,1,religion
শালী তোর কি কোন কাম নাই তুই তাহেরী হুজুরের ভিসা লাগবে বাইরে গিয়া ইউটিউব চ্যানেল কমেন্ট করে খারাপ নাস্তিক ইসলামের দালাল ম তুই এসব সাইরা ভালো কিছু কর তাহলে জাহান্নামের আগুন থেকে বাঁচতে পারবে যদি মুসলমান হয়ে থাকোস,1,religion
ফকিন্নি মাগির পুলারে পাছা দিয়া এসিড ঢুকাইয়া দেয়া উচিত 😡😡😡😠😡😠😡😠😡,1,religion
চরমোনাইকে।যে।ভন্ড।বলে।সে।জারোজ।,1,religion
এ ভাই আপ্নি জানুয়ারের বাচ্চা টিকই বলেচেন। কিন্তু এই সুদানির নামের পিচনে আপ্নি রাহমান লাগান কেন? ? আপ্নি জানেননা এই নাম আলহ তায়ালার একটা গুনের নাম।,1,religion
সব শালারা শুওরের বাচ্চা ইসলাম নিয়ে এই ধরনের কথা বলার সাহস পায় কেমনে,1,religion
জুতামারাউচিতবেয়াদোবেরদল খানকিরছেলেরাকিহাফেজনানাছতিক্যআমারমনেহয়নাটকশুরুকরছেইসলামনিয়েনাটক,1,religion
খানকীর পোলা এই পীর রে দেখলে মনে হয় হেতের গান্ডু দিয়ে ঝাঁটা ঢুকাই দেই। হেতের যারা পীর মনে করে এবং দেওয়ানবাগীর মুরিদ চোদাই ওরাও খানকীর পোলা।,1,religion
সব কটা নাস্তিক দের রাস্তায় রাস্তায় জুতা পিটা করা দরকার,1,religion
এইসব ভন্ড হুজুর কোথায় ওয়াজ করে হালার পো হালা তুরে পাইলে জুতা দিয়ে মারতাম,1,religion
মাদারচোদদেরকে যুতাপিটা করে দেশ থেকে তারাও,1,religion
তোদের দালাল তাহেরি তোর মাকে দিচে নাকি মাগির পুত,1,religion
কোতার বাচা একটা,1,religion
তুই এক নাম্বার নাস্তিক জারজ উহুদি নাফরমান তুই যেদিন আমার সামনে পড়বি সে দিন তোরে জুতা দিয়ে পিটাইতে পিটাইতে চাবার দাঁত পেলে দিবো বেয়াদব,1,religion
বলদ ভন্ড শালারপুত,1,religion
হাজি।সাহেবরা।জে।মাথানেরাকরে।ঐটাকি।অপরা।।।থর।কথায়।মনেহয়।।হাজিসাহেবরার।হজের।কনদামনাই।।থাইলে।সকল।হাজিরা।ইসলাম।ছেরে।মাথানেরাকরে।।হজকরতেজায়।।।কবরপুজারি।বন্ড।হারামি।।,1,religion
তুই জারজ অজাত আল্লামা হাফিজুর রহমানের কথা বুজার যোগ্য নাই,1,religion
এই দেওয়ানবাগি হল দাজ্জাল এর বন্দু,1,religion
শালা মাজার পুজারী কে ভালো করে পিঠা দেয়ার দরকার ছিলো,1,religion
তর মারে চুদি তরে ও চুদি তর বুনরে চুদি,1,religion
এ মাগিরা নাস্তিক ইসলাম নিয়ে মজা কর,1,religion
দেওয়ানবাগী হুজুর কে নিয়ে যারা এই সব প্রচার করতাছে তারা মানুষ রুপের শয়তান এরাই এজিদের বংশ ধর । এরাই রাজাকারের পুষা কুত্তা।,1,religion
মাদারচোদ এতো কথা বলিস ক্যা,1,religion
তোদের কি জন্ম কচু বাড়ীতে হয়েছিল যে সালা এই টিকটক বা আবিষ্কারক তার তো কোন মায়ের পেটে হয়নি,1,religion
আমি দেখেচি জুতা দিয়া পিডাই সালার পুতেরা বন্ড,1,religion
নাস্তিক কুকুরের বাচ্ছারা তদের মুখে জুতা।,1,religion
আগনিত ছিড়া জুতার বাড়ি এই কুত্তা না শুয়রের বাচ্চার দুই গাছে।। ধন্যবাদ সমাজ সেবক ভাই দোয়া ও ভালোবাসা।।,1,religion
এইসব ছাগলের বাচ্চাদের ফাঁসি চাই,1,religion
এই হালার ভাই এটা কি গান নাকি ভালো হইয়া যা।,1,religion
এই নাস্তিক দের কে মেরে মাটিতে পুতে দেওয়া উচিত,1,religion
তাহেরী বন্ড বদমাইস,1,religion
বলদের চেয়েও খরাপ তুই,1,religion
বালের উপস্থাপক।,1,religion
ওই শালা তাহেরি ওরে বাশ দেয়া হোউক,1,religion
ওই বুশকি মাগি ওখানে আসছে কে চোদা লওয়ার জন্নো,1,religion
বাংলাদেশে কিছু ভন্ড আছে যেমনঃ দেওয়ান বাগি আটরসি সুরেশ্বর মিরপুর মাজার গোলাপ শাহ মাজার লেংটা বাবা তাহেরি খানকির পোলা ফরিদ পুরী আরো অনেক এরা হলে মুর্খ মানুষ গুলো কে জাহান্নামে নিয়ে যাওয়ার রেলগাড়ি,1,religion
বানচোদ তাহেরি মুনাফিক তুই মিজানুর রহমান খুব ভাল মানুষ,1,religion
খানকির পোলারা ত্রকটা হুজুরেরে গালি দেছ,1,religion
তরে বরিশাল আসলে পিছা দিয়ে পিটাবো হারামি,1,religion
তাহেরি হারামজাদা।,1,religion
শালা তুই একটা শয়তান,1,religion
তোদেরকে কাছে পাইলে ঝাড়ু দিয়া জুতা দিয়া পিডামু,1,religion
মুতে লই বেজন্মার মুখে সবাই খারাও,1,religion
শালা তুই ভন্ড,1,religion
সালি লোপাকে,1,religion
কেয়ামতের আগে পর্যন্ত দেওয়ানবাগীকে পুটকিমারা উচিত,1,religion
দেওয়া বাগি এক টা জারজ খানকির পুলা,1,religion
আজা হারী কুত্তার বাচ্চা আর যে আজা হারীর পক্ষে কথা বলে সেই সত্যিকার অর্থেই মুনাফিক বেঈমান,1,religion
হারামজাদা গুলোরে দিয়ে মাথার গুলি করে উরিয়ে দিলে মনে শান্তি পেতাম😠,1,religion
আজকে শিওর হলাম তাহেরি বোকাচোদা।ওরে যে।আলেম মনে করে সেও বোকাচোদা,1,religion
এই বাচ্ছা পোলা তোকে আমি ভালো মোনে করতাম কিন্তু আমি ভুল বুঝেছি আসলে তুই যে তোর মায়ের জারজ সন্তান তা আমি জানতাম না আজ থেকে জানলাম সুধু তাই না তুই খাঁটি জিএমবি একে জরুরী তলব করতে হইবে,1,religion
ছাগল তাহেরী কুত্তার বাচ্চা,1,religion
জুতা মারা উচিত্ দেওয়ানবাগী শালা বাটপার জানোয়ার,1,religion
সালার বেটা শয়তান বাগি তোর কাচে গান্জা টা বেচে কেডা,1,religion
এই কুত্তার বাচ্চা দেওয়ান ভাগী একজন নাস্তিক,1,religion
সালারা টা কুত্তা,1,religion
মাগির পোলা দেওয়ানবাগী😡😡😡,1,religion
তোরে কে কয় তুই হুজুর তুইত বন্ড তুইতো মনে হয় জারজ কারন তুই তআরেক,1,religion
তাইরা ত এক মালাউন তা সবাই জানে,1,religion
সালা ছাগলা তারেহি,1,religion
কোন কুত্তার বাচ্চা বলে হাফিজুর রহমান ভন্ড মাগির পোলা তুই শালার পুত ভন্ড,1,religion
জ্ঞান হীন পশু যেমন তুমিও তেমন। তাই এই ভিডিও এডিট করে এখানে পোস্ট করেছো। তুমি এটা একবারও চিন্তা করলেনা যে সবাই তোমার মতো বলদ না। মাইক দিয়ে এই কথা বলবে আর সাধারণ মানুষ তাঁকে ছেড়ে দিবে। ঐ এলাকায় কি সবাই দেওয়ানবাগী হুজুরের মুরীদ? সবাই না আশে পাশে আরো অনেক সাধারণ মানুষ এবং প্রসাশন আছে। তুমি নিজেই আসলে কুকুরের বীর্যে জম্ম নেওয়া কুলাঙ্গার। নিজে ভাল হও। নিজের আকিদা ভাল কর।,1,religion
তুই ভন্ড সালা,1,religion
জারজ সন্তান।,1,religion
শালা তোর ভডামি বাদ দে তো দেওয়ান বাগকে আমি সামনে পেলে জুতা দিডে পিটাত,1,religion
দেওয়ানবাগীর মারে বাপ,1,religion
ওরা তো কুত্তার বাচ্চারা ভন্ড ভন্ড ভন্ড ফাঁসি ফাঁসি চাই,1,religion
আরে গাধার বাচ্চা এইসব তো এডিটিং করা ভিডিও,1,religion
ওই হারামির বাচ্চা জলহস্তীকে গালি দিয়ে নিজেদেরকে তার পর্যায়ে নামাতে চাই না কিন্তু না গাইলায়ে তো থাকাও যায় না একটা জিনিস জানবার চাই সে কোন ব্র‍্যান্ডের গাঞ্জা খায় এত্ত পিনিক পায় কেমনে কেমনে এত্ত পিনিক,1,religion
শালা কি ছারচ,1,religion
দেওয়ান বাগি কুত্তার ধন তোর মুখে ঢুকামু সালা,1,religion
সালা নাম্বার বন্ড বান্ডারী তার ওয়াজে সুদু কিচ্চা কাহীনি চাডা আর কিচু নাই। বেশি আলেম মনে করলে নিজেকে তাহলে কোরান হাদিস দিয়ে আলোচনা কর। এখন মানুষ সব বুযে এখন কিচ্চা কাহীনি চলেনা সত্য কথা সুনতে চায় কোরান হাদিস থেকে তার আসে পাসেও কিচু বন্ড লোক রাখচে তার কথায় হা বলার জন্য মানুষ এগুলো বুযে।,1,religion
জামাতপন্থী মওলবি রা সবখানে এমন ধোলাই খায়।সালা আহলে শয়তান মৌলভী,1,religion
দেওয়ানবাগীকে সরকারি ভাবেও কিছু করা যাবে না।কারন অনেক বড় বড় রাজনীতিবিদ বিজনেস ম্যান দেওয়ানবাগীর পোষা কুকুর,1,religion
মাদারচোদ তুই একট শয়তান,1,religion
এই পাগলটা কোন জানোয়ার যে ইসলামের বিরধে কথা বলে,1,religion
মুরগী চুরা কবির মাদার চুদের বিচি বারায় লাথি মারা দরকার ছিল,1,religion
মাদার চুদ তরে কিতার বাচ্চা,1,religion
সালা তাহসিন বদল তোর মতনি ভন্ড এরা দুই জনাই ভন্ড মাদারের বাচ্চা,1,religion
কুথার বাচছা তাহেলি হুজুর বসেন বসেন এই কারনে হারাপ আর বাস বাইয়া জগির করে বনডামি করে তাদের দেহনা তরে কি রেপ করছে নাকি,1,religion
শালা বাইনটোষ্ট।,1,religion
এই মাগি কে,1,religion
হুজুর প্রথমে আওলিয়াদের বিপক্ষে কথা বলেছে হুমকি দেওয়ার পর হুজুর আওলিয়াদের সুনাম বা প্রশংসা করতেছে।শয়তানি হুজুর।,1,religion
এই গিয়াস মাদারচোদ তুই পাচ কুটিটাকা কোথায় পেলি,1,religion
কাউয়া কাদের এত প্রশ্ন করার দরকার তোরে জনগণের ভোট দিছে কিনা। কাউয়া কাদের হাতে হলো একজন ভোট চোর। এত মানুষের কে রডের বদলে বাঁশ দে বিরিজের ভিতর।,1,politics
ওপু রেনডি মাগী,1,politics
কুত্তালীগের বিলুপ্ত চাই,1,politics
কাদের কাউ কাউয়া,1,politics
ছাগল কোথাকার !,1,politics
ভাই তুর যখন এতই চুদা খাওয়ার সখ নিজের ভোদা নিজের পুটকির ভিতর দেস না ক্যা??? শালা আমার বালের ইউটিউবার,1,politics
এ খবর দেয়ার জন্য মাগিরে চোদা লাগে এই মাগি বড় বেসা,1,politics
হিচা মার নটিরপো গো,1,politics
অপুর আলগা ভাতার কাউয়া,1,politics
মাগি তুর মারে চুদি,1,politics
রুমিন ফারজানার সাথে হিন্দু ধর্মের গাধার কথায় শুনে আমি কি জে বোলব বাসা খুঁজে পাই না ওপু কুকিল তুইতো রুমিন ফারজানার জুতার শোমান না ছাগলের সাথে থেকে ছাগলের মতো কথা,1,politics
কুত্তার বাচ্চা আওয়ামীলীগ কেনো তোরা জানোয়ারের মতো ব্যবহার করছিস,1,politics
এই মাগির পুর সাথে করে দুইটা মাগি নিয়ে ঘুরে এদের যখন তখন ব্যবহার করে শালা এখন বলছে এই মাগিদের নাকি উড়না নিয়ে টানাটানি করছে আর এদের নুর সহ তার সহযোগিরা সারারাত মাদক নিয়ে পরে থাকে।,1,politics
ছাএ লিগ সন্ত্রাসী ।।। জয় বাংলা।,1,politics
কাউয়া কাদের পরমোশন পাইয়া এখন ঘড়ি কাদের।,1,politics
কুত্তালিগের আস্তানা জালিয়ে দাও পুড়িয়ে দাও,1,politics
ওই নোমো মাগিরে আনছে কে ওখানে লুচ্চা কাদের,1,politics
দুর কুকুতার বাচচা ইনু,1,politics
পশাসন কুত্তালীগের পা চাটা কুত্তা,1,politics
এ মাগিদের দুদ টিপিদে ভাল করি।,1,politics
চোরের মা খালেদা জিয়া হাওয়া ভবন খালেদা জিয়া অষ্টম শ্রেণি পাশ খারেদা জিয়া গোলপি বেগম জিয়া😆😆😆,1,politics
বেগম জিয়া শেখ সাদী আর কাউয়া হলো বকরির লাদি।,1,politics
চুদায়ছে শালা কাওয়া কাদের,1,politics
বিএমপি চোর,1,politics
খানখির পোলারা কুত্তালিগের দালালরা ভালো ত্রকজন মানুষের বাংলাদেশের জায়গা হয়না নুরকে কেনো মারলি খানখির পোলারা,1,politics
হারামি সরকার হাছিনা।,1,politics
কাউয়া কাদের ভাই,1,politics
সেএকটা মিথ্যাবাদি শেখ হাচিনার পোসা বেজী।,1,politics
সব নায়িকারা চুদা খাইয়া জনপ্রিয় হয়।,1,politics
কুওা লী কে জুতা মারা হোক,1,politics
তারেক জিয়া তুরে চুদেছে,1,politics
তে কেমন স্যার আগে স্যারকে মার সব ঠিক হয়ে জাবে স্যার হলো মাদারচুদকে কোনঠাসা করলে ভাল হবে,1,politics
এই মালা উনের বাচ্চা কে জিন্দা পোরা উচিত,1,politics
ওদেরকে কুত্তা লীগ বললেও কুত্তায় মাইন্ড করবে ৷ কারণ কুকুরেরও একটা সম্মান আছে ৷,1,politics
কচি মেয়ে খাওয়ার অভ্যাসটা কাওউয়া কাদেরের আর গেলো না।,1,politics
ছাএলিগ হলো বাংলার বাষ্টাড জারা ছাএলীগ করে তাদের জম্নের ঠিক নেই বাবার পরিচয় নাই।,1,politics
ওবায়দুল কাদের হচ্ছে একজন কাউয়া,1,politics
তুই হালায় মাইর খেয়ে ই মরবি,1,politics
মালুকে পেলে চুদতাম,1,politics
অপু উকিল মালাউনের বাচ্চার পাওয়ার বেড়ে গেছে,1,politics
কুত্তা লীগের একদিন পতন হবে বাংলার জমিনে ইংসা আল্লা,1,politics
এটা শিক্ষক না এটা খানকিৱ ছাওয়াল এ শিক্ষক জাতিৱ কলংক এৱ মুখে মুখে লাথি মাৱা দৱকাৱ,1,politics
রুমিন একটামাল ওওও যদি একবার চুদ তে পারতাম,1,politics
কাউয়া কাদেরের সাথে কখনো খালেদা জিয়ার তুলনা হয় না,1,politics
এই মাগী তুই কি বেশী বূজস শালী,1,politics
সালার পুতেরা জনগনের রক্ত পানি করা টাকা দিয়ে ফুটাঙ্গিরি চোদায় মাদারচোদ দুর্নীতিবাজ এগুলারে গালি দিতে ওরা বাধ্য করে এসব দুনীতিবাজদের জন্য মার্জিত কোন শব্দ অাসেনা প্রযোজ্যও নয়,1,politics
ছাগলের সাথে বাংলাদেশের সবছেয়ে জনপ্রিয় নেত্রী সাবেক সফল প্রধানমন্ত্রীর সাথে তুলনা করে যারা তারা মনে হয় গাধার ঔরশজাত,1,politics
লুচ্চু কাদের,1,politics
মাদারেরে বাচ্চা অপু কয়,1,politics
এটা কয় তারিখের কাহিনী একটু কমেন্টে জানাবেন+ভাই কী বলবো বলার ভাষা নেই শেখ হাসিনা একটা কুত্তী ওর পুরা চরিত্র টাই কুত্তী ছাত্রলীগের সন্ত্রাসীরা সবগুলো জারজ সন্তান ওদের মাথায় হীতা হীত জ্ঞান বলতে কিছু নেই কিভাবে ওরা ডিম টিম এইসব জিনিস কিভাবে মারলো,1,politics
চোরের মায়ের বড় গলা উপু উকিল তুই,1,politics
য়েয় এই কথা গুল বলল সে একটা পাকা খানকি মাগীর ছেলে ওর টাকা কত আছে তুই জানবি কি করে তুইত একটা কাউ কাদেরের পা চাটা কুতা,1,politics
কুকুরের বাচ্চাদের ছোট ছোট দলকে একত্রে ছাত্রলীগ বলা হয় উল্লেখ্য তাদেরকে বালের কর্মীও বলা হয় এরা নিসন্দেহে হারামজাদা এদের বাবার ঠিক নেই।,1,politics
কোথায় আগর তলা আর কোথায় ওগঊর তলা হিন্দু কুলাঈারের সাথে কেন যে নিয়ে আসে চেনে লের লোকেরা আমার বুজে আসেনা,1,politics
কুওালীগ দলটা নিষিদ্ধ করার দরকার,1,politics
রমিন ফারহান হলো বিশশা মাগি।,1,politics
তোমরা ভাল চিরনি সালার পুরেতা সালার পুতেরা হাতে একটা করে বাস নিয়ে কুত্তালীগকে বাইরিয়ে ইন্ডিয়া পাটিয়ে দিতে পারনা সালার পুতেরা শুদু চাপাবাজি কর,1,politics
লীগ মানেই পতিতার জন্ম,1,politics
কাওয়া কাদেরের কিসের সতোতা,1,politics
কুম্ভালিগ।দৈরা।জোতামার।,1,politics
এই শালা নোয়াখালাই বড় মাদার চোদ,1,politics
অপু উকিল এটা কি মুসলিম না হিন্দু বুঝ যায় না মনে ত হিজলা,1,politics
অপু উকিল জাতীয় বেশ্যা । তার অতীত ইতিহাস ভার্সিটি তে দেহ বিলিয়ে পদ বাগিয়ে নেয়া!,1,politics
ওই খানকির পুলা তুই বালএর কাছে যাইতে প্যারিশ তুই ইসলাম ধর্ম নিয়ে মন্তব্য করিস তোরে বাংলাদেশে যদি আমার সামনে পাই কখনো জোত দিয়ে তোর মুখ হারায় দিবো,1,politics
হায়রে মাদারচুদলীগ দেশটারে ধংস করে দিল,1,politics
ছাত্রলীগ নামে কুক্তার বাচ্চাদের যেখানে পাবেন কুক্তার মত পিটিয়ে মারবেন,1,politics
এরা হলো চুদার লীগ,1,politics
আওয়ামিলিগের মারে চুদি,1,politics
আরে মাগী তরও জায়গা নাই আলীগে,1,politics
জন গণ বালের লীগকে চাই না,1,politics
ডিম দিয়া পাছা মার শালা নুরাকে,1,politics
পুরোই আবাল,1,politics
উপু তুই মাগি মিথ্যা কথা কছ,1,politics
বিশ্ববিদ্যালয় মানে খানকি পাড়া।এখানে আর একটা লাকির মত খানকি জন্ম হবে,1,politics
যখন খালি যোগাযোগ মন্রি ছিলেন তখন ওবায়দুল কাদের কে আমিও অনেক ভালোবাস তাম তার কাজ দেখা বর্তমানে সে লাগামহিন কথা বলে তাই থু থু মারি হারাম জাদাকে।,1,politics
লিগের কুক্তি ওবাদুল কাদের তোরে কয়বার চুদেচে জনগণ জানতে চায় বিশ্ব মাগি,1,politics
খালেদা জিয়ার মতো একজন মানুষের সঙ্গে কাউয়ার মতো লোকের তুলনা দেয় মূর্খের দল,1,politics
এটাই জুতালিগ চোর লিগ,1,politics
কাদের কাওয়া নামে পরিচিত বেগম জিয়া আপোষহীন দেশনেত্রী তিনবারের প্রধানমন্ত্রী। কোথায় বকরীর লাদি আর কোথায় শেখ সাদী।,1,politics
কোথায় কাউকা কাদের কালা মিয়া আর কোথায় খালেদা জিয়া।আর এই ছাগীটা সুনাম করতেছে কাউয়ার কথা কাউয়াকে যেন জাতি চিনেনা।,1,politics
ডিম দিয়া পাছা মর শালা নুরাকে,1,politics
কুত্তালীগের লাইসেন্স নাই সবাই জানে এই কুত্তালীগ রাস্তাই নেমে কি শুরু করেছে ।।।।।।।,1,politics
জারজ লিগ মানুষ হলি না,1,politics
সবাই এখন কুত্তলীগ করে,1,politics
জায়েদ খান একটা বলদা।,1,politics
কাওয়া কাদেরের পাব্লিসিটি স্টান্ট !!!!!!!!!!!!,1,politics
সালায় একটা পাগল! মাথায় সমস্যা আছে!কাউয়া কাদের!,1,politics
কুত্তা লিগ,1,politics
সব রেন্ডিয়ার মালুদের দালাল,1,politics
অপু উকিল একটা মাগী!নির্লজ্জ মিথ্যাচার করার জন্যই এই চরিত্রহীন নারীটা টকশো তে আসে!,1,politics
কাদের কে কুত্তা দিয়ে চুদাও,1,politics
কাউয়া কাদের সাথে তুলনা করে আবালের দল।,1,politics
আমলা পাড়ায় নায়িকা মডেল ও নায়ক এদের দেহ ব্যবসা শত হাজার বছরের পুরোনো কিন্তু নায়কদের যে টাকার বিনিমিয়ে পুটকি মারে বিষয়টা গোপন রয়ে গেল মিডিয়ার যে অবস্থা বিষয়টা ফ্লাস হলে ভালো চলত শাকিব ফেরদৌস জায়েদ রিয়াজ আরো যারা আছে ক্যামেরা চোখ রাখো পাবে,1,politics
আওয়ামিলীগ এর জারজ মন্ত্রীরা জনগনের টাকা মেরে এসব শখ মিটাচ্ছে। শালা কুকুর লীগ।,1,politics
কুওা লীগের চামচা অপু 👠👠👠👠👠👠👠👠👠👠👠👠👠👠👠👠,1,politics
কুত্তা লীগ মিথ্যা কথা আর কতো বলবি,1,politics
এদেরকে ছাত্রলীগ বললে ভুল হবে কুত্তালীগ বলে,1,politics
খালেদা জিয়া তো এতিমদের টাকা খেয়ে ফেলে জেলে আছে । চোরদের বড় কথা কিন্তু কেন। তোদের রাজনীতির দলের মাকে ঘন ধর্ষন করার দরকার। আর এই মাগীকে ঘন ধর্ষন করার দরকার এক বছর।,1,politics
কুকুর কাদের।,1,politics
এই সালা কউয়া নাতকি হারামি কুতা বাইচচা,1,politics
কোন ছুদাউরির ছাত্রলীগে নুর ভাইরে হামলা করে। ফাটাইলিমুনু,1,politics
হিন্দু সালি পাগলি,1,politics
বালের লীগ,1,politics
তারেক কে জুতা মার,1,politics
নুরুকে জুতাপিটা করাহক নুরু কুতার বাচচা,1,politics
চটি বই লিখে রয়্যালিটি পান আর কি চোর শুয়োরের বাচ্চা ৷,1,politics
কুওালিগকে ঘৃনা কোরি ওদের কারোনে দেসে এতো গজোব,1,politics
অবদা কাদের ত ফাগল,1,politics
এই খানকির বাচ্চা বোঝেনাযে ছাত্রলীগ-যুবলীগে এগুলো করছে,1,politics
এই কুতা লিক ছাত্রদে খারনে আমাদের ছেলে মেয়েদের আর পড়াতে ইচ্চাকরেনা পরতে গেছে না সত্রারাশি করতে গেছে এইটা কিরকম শিক্কা এ বাংলায় এসব শিক্কা রাজনিতি বন্দ করাহোক,1,politics
কাদের টিকমত কথাই বলতে পারেনা ওরে আবার মন্ত্রী বানাইসে। শালা একটা গন্ডমূর্খ।,1,politics
রুমিন মাগী তুমিতো আত্মস্বীকৃত মাগী। কারণ দীর্ঘ মাস তারেক ডাকুর সাথে রাত যাপনেই তাই প্রমানিত।ধিক্কার পুরাতন মাগী।,1,politics
মুর্খ আবাল,1,politics
কাউয়া কাদেরকে বাদ দেওয়া উচিৎ।,1,politics
জারা ছাএলীগ করে তাদের জন্ম হইছে কনডম দূর্ঘটনায়,1,politics
পাগলে কি বলে কিছু ই বুজলাম না । কোথায় খালেদা জিয়া আর কোথায় কাউয়া। সুষ্ঠু নির্বাচন হলে কোন দিন কাউয়া এম পি হতে পারে না।,1,politics
ব্যাশা মাগি অপু কে সেফুদার কাচে পাটিয়ে দেওয়া উচিৎ।,1,politics
কুত্তা নুরু খেলা শুরু হয়েছে তোর,1,politics
কুত্তার বাচ্চারা ভাগাভাগি করছিস শুয়োরের মাংস নিয়ে???,1,politics
কুত্তালিগী অপু উকিল তোরে বাঁশ দেওয়া হবে মিথ্যে মিথ্যে সব কথাই মিথ্যে বাস্টার্ড জানোয়ার।,1,politics
পরিষ্কার একটা সন্ত্রাসী কান্ডকে এই শালা দালাল প্রভোস্ট ভূলবুজাবুজি বলে চালিয়ে দিতে চাইল। ছাত্রসমাজ জাগো। না হয় এই হারামজাদাগুলা একদিন সব চিবিয়ে খাবে। জাগো! জাগো! জাগো!,1,politics
বেগম খালেদা জিয়ার সাথে কাউয়ার তুলনা? এইটা হাস্যকর এইটা জনগনের জন্য সত্যিই হাস্যকর 😀😀😀😆😆😆,1,politics
বুঝেছি তোরা কিনতে পারিস না তাই কাদের সাহেব টা দেখে তোদের অনেক নিংসা হয়েছে হায়রে মাবুদ এখন হাতে ঘরি পড়লে দোস মাদার চোদ বি এন পি জামায়াত তোরা কি শুরু করলি,1,politics
খানকির পুলা ভালো নাটক করতে পারে,1,politics
সব গুলো জারুজ সন্তান কুকুরের ছোদা,1,politics
ওই খানকির পোলা বাড়ানোর জন্য আর কত মিছা কথা কবি,1,politics
ভাই তুমি একটু সতর্ক অবলম্বন করো । না হয় কুত্তালীগ কামড় মারবে ।,1,politics
জানুয়ার মানে বি এন পি কুতার বাচচা মানে বি এন পি জারজ দল মানে বি এন পি ছাএদল মানে জারজ দল,1,politics
অপু উকিল একটা পাগল মহিলা এবং হিজলা মহিলা,1,politics
কুওাদের সাথে কুওার মতো আচরণ করাই দরকার।।।।,1,politics
বাংলা এক নাববার খারাপ মহিলা খালেদা জিয়া কাদের স্যর বাংলা খুব ভালো মানুষ,1,politics
অপুউকিলতরমায়েচুদিমাগিমিতাবাতী,1,politics
হাসিনার পা চাটা কুত্তি এত বড় বড় কথা বলিস হাসিনা তোরে কোন পদ দেয়নি কেন হাসিনা তোরে পাদ দিবে পাদ,1,politics
কুত্তালীগের কুত্তার বাচ্চারা তোরা রেডি থাক তোদেরকে কবর থেকে উঠাইয়া মানুষ জুতা দিয়ে পিটাবে।,1,politics
কুত্তালীগের বাচ্চারা আসলে কুত্তার বাচ্চা ওরা শুয়োরের মাংস খায় ওদের দয়া মায়া নেই শালার বদমাসের দল,1,politics
অপু তোকে আমি চুদি,1,politics
হায়রে উকিল! যুক্তিতে না পেরে পাগলের প্রলাপ বকতেছে তোক আসলে ক্রিস গেইল কে দিয়ে চোদানো উচিত।,1,politics
কোন কুওার বাচ্চা আমার নের্তির সাথে কাউর তুলনা করে। ওখানে হাসিনা আসলেও কাম হবেনা,1,politics
কাুউয়া কাদিরের মত লোকদেরকে ট্যাপিকের কাজ করাতে হবে ভবিষ্যতে এই কারনে পসিখন দিচেছ,1,politics
মিথ্যাবাদীর জনক হলো কাউয়া কাদের,1,politics
এই মহিলা কি আবাল নাকি যে অসুস্থ সে দেশ চালাবে আবার কি এটা কি এই মহিলা বুঝে না এই মহিলা পুটকি দিয়ে পাহাড় ঠেলেই তো আর হবে না !!,1,politics
কাউয়া কাদের শেস,1,politics
নুরু জারজ বাচচা কে পাকিতান পাঠানয় হক জারজ বাচচা নুরু,1,politics
মাগি তুই কতো জনকে চুদা দেয় সাংবাদিক হয়েছো,1,politics
রুমি মেডামের সাথে যে পতিতা লীগ সরকারের হয়ে কথা বলার জন্য আসছে তা তো কোন ভাবেই মানা যায় না কারণ রুমি মেডাম একজন শিক্ষিত ও খ্যাতি অর্জন কারি নারী । আর এই পতিতা তো রুমি মেডামের বাড়িতে কাজের মেয়ে হিসেবে ও মানায় না কি বলেন বাংলাদেশের জনগণ ?,1,politics
নুরা হালারে মার,1,politics
ছাএ দল মানে জারজ দল,1,politics
এই আওয়ামীলীগের মাগী বুঝেনা দেশটা যে শেষ করে দিছে মিথ্যা বলে।,1,politics
কাউয়া কাদের আর হিরো আলোম ছেইম,1,politics
ছাএ লিগের মাইরে বাপ খাংকির ছেলেরা কোন দিন মানুষ হবে না।,1,politics
ঐ খানকি মাগি তারেক রহমান তোরমতো মাগিরে চুদে নায় তো,1,politics
কুত্তালীগ যতদিন থাকবে দেশ কখনো ভাল হবে না।ক্ষমতায় টিকে থাকার জন্য রাষ্ট্র সম্পদ ভারত কে দিয়ে দিতে পারে অন্যায় ভাবে মানুষ খুন করতে পারে। এটা কেমন দেশ।,1,politics
বাংলাদেশ টাকে।নরক।বানিয়েছে।হাছিনা।এই।মাগীরে।গদিথেকে।নামান।সবাই।,1,politics
সব গুলি দেখতে মালুর মত। একটা দেখে মনে হয় না মুসলমান দারি টুপি ওয়ালা নেই। সব মাউরার দল,1,politics
সালা খানকির পুলা দেশটা কে খেয়ে দিলো খানকির পুলা কাউয়া,1,politics
হিজড়া ও তোতলা কাক কাদের সাহস করে কুত্তা কুত্তির দলের লাইনে দাঁড়িয়ে পুরুষত্ত্ব দেখাতে চায়!,1,politics
সাংবাদিক সালারাদের পিডা ওরা ভিডিও কাট করল কেন।,1,politics
কাওয় কাদের মরলে কুততা যবে করে জানোয়ার দের খাওয়ানো হবে কেন না কাদের একজন সন্ত্রাসী স্বৈরাচার জানোয়ার,1,politics
পাগলা কাদেরের সাতে বেগম জিয়া কে মিলালো কোন পাগল,1,politics
বালছিরা তুইও কারো কাছ থেকে একটা চেয়ে নে।,1,politics
চোর জন্ম দেওয়া খালেদা চুরির দায়ে জেলে হা হা হা,1,politics
শেখাসিনা খানকি মাগি এখোন আর দেখেনা ওর ছামা আর চুলকায়না,1,politics
শালা তুই ওবায়দুল কাদেরের বেডরুমে ঢুকেছিস কেমনে?,1,politics
দোর সালা মাগির পোত,1,politics
কুএালিগ সখানেই গেওগেউ করে,1,politics
আওয়ামী লীগ ভোট চোর লীগ যুবলীগ ক্যাসিনো লীগ ছাত্রলীগ কুত্তালীগ,1,politics
বালের ভিপি।,1,politics
তরা চোর যে আসবে সেওচোর হবে,1,politics
মন্ত্রীরা সব হারামজাদা আস্তো বদের ধাড়ী,1,politics
হাসিনার চামচাতো কথাই বলতে পারে না।।,1,politics
কোটি কোটি টাকা চুরি করে বড় বড় কথা বলে এদের লজ্জা বলতে নেই।এরা রেন্ডির দালাল।,1,politics
এবার দেখবেন নিশ্চয়ই কোন মালাউন কে সাধারণ সম্পাদক বানাবে।দাদা কে খুশি করার জন্য।,1,politics
এ দেশে চোর ছারা কোন কুততার বাচচা আছে জে কুততার বাচচা রাজনিতি করে,1,politics
সব আওয়ামীলীগের পা চাটা কুত্তা,1,politics
এই শালি এমন ভাবে কথা বলে তা শুনে মনে হয় রাতে তার স্বামি তাকে সুখ দিতে পারেমি তাই মেজাজ খিটখিটে অবস্তা।,1,politics
আওয়ামীলীগ আর হাসিনা বাংলার ফেরাওন আর ছাগল কাদের কাওয়া 👣👣👣👎👎👎,1,politics
ওবাদূল।কাদের।একজন।কাউয়া,1,politics
সালার পাগল ওবাইধদুল যে কাজ পুলিশের সেই মগা করে,1,politics
লিগের বাচ্চারা আসলে কুল্লাগারের জাত,1,politics
বেগম জিয়ার সাথে কাউয়া চোর চোরটার তুলনা ছি ছি ছি মোনাফেক হাসিনা।,1,politics
লুচ্চা কাউয়া কাদির আর ভালো হইলো না,1,politics
নুরুল তোর মরন আসছে বেশি লাফা লাফি করিছ না পকিনির পোলা তুই শেখ মজিব হতে চাস।,1,politics
অবৈদলীগ ভোটচুরলীগ কুত্তালীগ,1,politics
শিক্ষকরা সব কুলাঙ্গার হয়ে যাচ্ছে দিন দিন!,1,politics
কাদের কাওয়া নামে পরিচিত বেগম জিয়া আপোষহীন দেশনেত্রী তিনবারের প্রধানমন্ত্রী। কোথায় বকরীর লাদি আ,1,politics
অপু উকিল কে আমি পুটকি মারতে ছাই,1,politics
আওয়ামিলীগ মানে কুওা চুদা,1,politics
হিন্দু মহিলা বাংলাদেশে কেন,1,politics
তুই রাজাকারের বিবির বাচ্চাদের ভিপি মুক্তিযুদ্ধা সন্তানদের নয়? পচা ডিম হল তুর তিরস্কার,1,politics
বাংলার মানুষ বাংলা ছবিকে হোন্দাইনা কাউয়া,1,politics
কুত্তার বাচ্চারা তোরা কি বিশ্ববিদ্যালয় পড়ালেখা করতে আসছিস না রাজনীতি করতে আসছিস।,1,politics
চোদানী মাগী আয়ামীলিগের নেতির তর কথাই তো হয়না মাগি,1,politics
কুত্তা কাদের,1,politics
শেষের মাগীর নাম কি যানিনা আরে সালি কার সাথে কার তুলনা দিয়েছিস ভুট চোরি করা দল কাদের তো খারা একটা মাদারচুত এর কথা কোনো মোল্য নেই কিসের মধ্যে কি আর পান্তা বাতে ঘী,1,politics
ছাএলীগ নামটা শুনলে মনে হয় নামটার গায়ে মুতে দেই,1,politics
চোরের মা খালেদা। সবার থেকেই আলাদা।,1,politics
খালেদা জিয়ার সাথে কাওয়ার তুলনা হা হা হা কুত্তায় মরলো না কেনো? খালেদা জিয়ার মুক্তি চাই কুত্তা লিগ নিপাত জাক,1,politics
বোদাই তুই অপুকে চিনস না?,1,politics
এই সব কুলাঙ্গারদের উচিত শিক্ষা দেয়া উচিত।,1,politics
ওবাইদুল কাদের একটা।ভোদার।মাথা,1,politics
কুততা কাদেরের সাথে বেগম জিয়ার তুলনা হয়না,1,politics
ঘটনা সত্য আপনি একটা রাম ছাগল 😡 যদি কোন বেরিফাইড চ্যানেল এর রেফারেন্স দিতে পারেন তা হলে মনে করবো আপনি মানুষের কেতারে পরেন,1,politics
আম্লিগ চোর,1,politics
সব কুত্তা রা কুত্তালিগের পাচাডা কুত্তা,1,politics
এই মাদার চোদেরা ছারের উপযুক্ত না ওদেরকে লেংটা করে কলেচ থেকে বের করা হোক,1,politics
কাউয়া কাদের ওইডা হইছে কাউয়া কাউয়া।তার সাথে কার তুলনা করতেছে গনতন্ত্রের? বাংলাদেশের?😁😁😁।খুবই হাসি পাইলো।কাউয়ার কি যোগ্যতা আছে?ও কে? যে ওর সাথে আপোষহীন নেএী তিন বারের প্রধান মন্ত্রী গনতন্ত্রের জননীর তুলনা দিতে হবে। রুমিন আপু অনেক অনেক ধন্যবাদ উপযুক্ত জবাব দেওয়ার জন্য।,1,politics
আরে আওয়ামী লীগ এর বাচ্চারা তোদের কি কোন শিক্ষা হবে না? ছাগলের প্রস্রাব এবং গরুর প্রস্রাব দুইটা মিক্স করে সকালে এবং বিকেল বেলা খালি পেটে খা? তাহলে তোদের বুদ্ধি হবে কাউয়া কাদেরের কুরুচিপূর্ণ চেহারা দেখে এখনো তোদের শিক্ষা হলো না!,1,politics
পাগল ছাগল কোথাকার,1,politics
কাদের হারামজাদা,1,politics
হিন্দু একটা খানকি,1,politics
সাওর মাগি তুইত যানিসিনা ইতিহাস কাও মাগি আপু,1,politics
এই স্যার কুত্তার বাচ্চা আর এক কুত্তা লীগ। সালারে জুতা মারো সবাই।,1,politics
আওমিলিগ এর আকাডা খানকি কোন বালের মাথা কইলো কিছুই বুজলাম না মাউল্লাএ বাচ্চা,1,politics
সময় চলে যায় বাল পেকে যায়। বিচিও ঝুলে যায়। কিন্তু ছাত্রলীগের এই চোদনারা আজীবন আচোদাই রয়ে যায়।,1,politics
বাল ফালানোর জন্য ছিলা সেখানে মাগিটা এতো বলছে আর তুমরা চুপ।চুড়ি পরে থাকো ঢাকা বিশ্ববিদ্যালয় ছাত্রলীগ।,1,politics
হিন্দু মাগিটা কে চোদতে ভালো লাগবে,1,politics
চোরের গোষ্ঠী নামছে চোর ধরতে । শালা আবালের দল ।,1,politics
মাগির জি এইটা কোন খবর হল,1,politics
হিন্দুর বাচ্চারে জুতা মারা হক,1,politics
অপু কে চুদতে চাই গুদের জোর দেখতে চাই।,1,politics
খানকি তোরা তো সব সময় ভোট চুরি করে খমতায় গেসোচ খানকি😠🔨,1,politics
ছাএলীগ কুকুরে লীগ ফেরাউনের দল,1,politics
বেগম জিয়া ছিলো পাকিস্তান এর রাতের খাওয়ার তাহলে কি ভাবে ওনি বাংলাদেশের প্রধানমন্ত্রী হোন ওনি তো পাকিস্তানের প্রধানমন্ত্রী হওয়ার কথা তোদের বেগম জিয়া যেমন ম্যাগি তোরাও ম্যাগি,1,politics
ঐ টিচার কুত্তালীগের মদদ দিচ্ছে,1,politics
খালেদা জিয়ার সাথে কাউয়ার তুলনা হবে না ইতি হলো একটা মাগি ইতিরে শেপুদার কাচে পাটাই দেন,1,politics
পাশের দেশ নোয়াখালীর কাউয়া কাদেরকে রাখেন দল থেকে পরিষ্কার করলে কাউয়া কাদের পাগল হয়ে যাবে সে যেন আরো কিছুদিন মাগীবাজী করতে পারে সেই সুযোগ দেন😃😃😃,1,politics
অপু উকিল এটাতো একটা মাগি,1,politics
ওবায়দুল কাদেরের জাঙ্গিয়ার দাম মনে হয় লাখ টাকা করে শালার কাউয়া কাদের,1,politics
তুই তো মাগি ওপু,1,politics
খানকীর পোলার গো নাটক দেখলে অামার ধন কাড়ায় যায়,1,politics
ওবায়দুল কাদের একটা পাগল সালা পুত ও মাথা ঠিক নাই,1,politics
লুচ্চা কাদের,1,politics
কাউয়া কাদের কাকা করবেনই এইটাই স্বাভাবিক উনাকে দেখলে কাউয়া কাকা বন্ধ করে দেই আমার মনে হয় উনিতা নিজে ও জানেন না 🤔,1,politics
বিএনপির মাগীরপোলাড়া।খালি।উইটিইবে।কুততারমতো।ঘেউঘেউ।করে,1,politics
হিন্দুর বাচ্চা কি বলে,1,politics
কাওয়া কাদের আবার কি এমন লোক,1,politics
ওবায়দুল কাদের একটা বড় লম্পট ও লুচ্চা। সবসময় নায়িকা খাওয়ার ধান্দায় থাকে।,1,politics
কাওয়া কাদের জাহ কোরোচ মোন পাবিনা।সোরকারি গারি কোওডা দোর চোওচ। বেদোপ,1,politics
ছাত্রলীগ মানে বর্বর অসভ্য । ছাত্র সমাজ এই বেয়াদবদের রাস্তার কুকুরের চেয়ে ও নিকৃষ্ট ভাবে।,1,politics
কুত্তালীগ অত্যাচার কবে বন্ধ হবে,1,politics
আওয়ামী বাইনচুদদের ব্রাষ্টফাইয়ার করে জাহান্নামে পাঠানো দরকার 😠,1,politics
আরে ভাই এটা আমার নানি সেকহাসিনার কুকুর লিগ,1,politics
এই শিখখকক একটা শুওর এদের মেরে ফেলা উচিত,1,politics
আওয়ামীলীগে মানে জানোয়ার হারামজাদা জারজ কুত্তার বাচ্চা শুয়োরের বাচ্চা ভারতের দালাল,1,politics
পতিতারা লিডার হওয়ার জন্য কাউকে খুশী করতে চায় সে কোন ভাবে হোক। আর কাউয়ত মন চায় এ সব কচি কচি খুকীদেরকে,1,politics
এই কুকুরের বাচ্চা নুরার কারনে শিক্ষার পরিবেশ নষ্ট।,1,politics
তার বাপের টাকা🐕 বাচ্চার,1,politics
এই কাওয়া কে দেখলে মেজাজ খারাপ হয়ে যায়,1,politics
খুনি ভারতীয় দালাল হাসিনা এবং কাউয়া কাদের কে কিভাবে তুলনা দেন আপনারা দেশ নেএির সাতে,1,politics
ওপুযে পাগল আর হিন্দুদে যে হারাম খাওয়া জায়ে আর ভোট চোর কারা জনগনকে জানে আর জনগনকে ভোট দিবারদে চোরকে তখন বুজা চোরে মা বড় গলা দিনে ভোট রাতে দেছ আবার বড় বড় কথা আর আয়মিলিগে হারাম খাওয়া জায়ে,1,politics
হিন্দু মাগিটাকে সেফুদার কাছে পাঠিয়ে দিলে বুঝবে রাজনিতি কি জিনিস,1,politics
অপু উকিলকে দেখতে টাকার পতিতার মত লাগে।,1,politics
ঐ সময় মাদার চুদ পুলিশ কোই ছিলো,1,politics
তুর জামাতের মারে ছুদি। বিএপির সবাই হিজড়া,1,politics
বাংলাদেশ মানুষ পসুর সমান,1,politics
দেশের জঙ্গি মত ছাত্র লীগ,1,politics
কুত্তার বাচ্চারা টাকা দিয়ে ফ্যাশন শো করে আর আমরা খাইতে পারিনা,1,politics
ও সালা দালাল এর জন্য ওর ভাল লাগতাছিলো না তাই তারা তারি শেষ করে দিলো,1,politics
লুচ্চা কাদের! কই উগইর তলা আর কই আগরতলা!,1,politics
কাঊয়া কাদের হলো একটা হিজড়া এবং নাস্তিক এই হারামির কাছ থেকে আর কি আশা করা যায়? যাকিছু করতে যায় সবই লোক দেখানো সে মনে করে পাবলিক বুঝেনা কত বড় বোকা সালা আমি যেখান থেকে দেখছি সে যে কোথায় গিয়ে গা ডাকা দিবে আমার জানা নেই যেখানেই পালিয়ে যাক না কেন তাকে বের করে ইচ্ছেমত পেঠানো হবে সেই সময় আর বেশী দিন নয়,1,politics
কাউয়া কাদের সাহেব একজন সেতু মন্ত্রী রডের বদলে দেওয়া হয় বাঁশ সিমেন্টের জন্য দেওয়া হয় কাঁদা মাটি উদ্বোধনের আগেই ব্রিজ ভেঙে যায় বুঝতেই পারছেন এতো দামি ঘড়ি গুলো কোথায় থেকে এসেছে ???,1,politics
ছাত্রলীগ একটি সন্ত্রাসী সংগঠন ছাত্রলীগের গালে গালে জুতা মারো তালে তাহলে এরা সাধারণ মানুষের জন্য বড় ধরনের হুমকি,1,politics
মালাউন খানকি ডায় হাসে,1,politics
সারা পৃথিবীর ভিতরে নোয়াখালী মানুষ মাদারচোদ নাম্বার ওয়ান,1,politics
শুয়োরের বাচ্ছা বহুত বড় অভিনেতা শালারে সামনে জবাই করতাম।,1,politics
কাদের ধনের মাথা চোর কাদের একটা ফাটা কেষ্ট কোই রাজ রানী আর কোই চোর বন্ড পাঘলা কাদের বেগম জিয়া মানে বাংলাদেশ,1,politics
অপু এজটা খানখি মাগী তার মারে চোদদাম খানখির চোখে ঠেডা পরচে ব্যাংকের হাজার কোটি টাকা পাচারকারীরা এখন কোথায়,1,politics
আবাল মন্ত্রী,1,politics
চুতমারানি তুই বিদেশে কেন? দেশে আয়,1,politics
এই ও কুতা লীগের কুতা স্যার,1,politics
নামকরা মাগী অপু উকিল,1,politics
শয়তান তো শয়তানের জায়গায় থাকবে এটা আবার নতুন কি পুরা লীগটাইতো শয়তানের লীগ ! হাস্যকর,1,politics
ওরে চোদনা । তুমি আমেরিকা থেকে এতো কথা বলতেছো ।,1,politics
আমার মনে হয় অপু উকিল খানকি মাগী কি কাউয়া কাদেরের চুদা খাইছে।,1,politics
কাদের একজন ছাগল আর বেগম খালেদা একজন দেশও নেত্রী,1,politics
কাফেরের বাচ্চা ওপুর মুখে জুতা মারি মিথ্যা বাধি কাফের,1,politics
তোদের এইসব লেংটামি দেখার মানসিকতা ও সময় % মানুষের নাই এই কথাটা না বুঝলে অমানুষ তোরা।,1,politics
হাসিনা হলো মাগী আর কুত্তা লীক মাদারসুদ আমি কোন দল করি না,1,politics
কাউয়া কাদেরের ইলিগেল বউ মনে হয় এটা তাই এতো সম্মান সম্মান মারায়!এই কুত্তার বাচ্চায় কার সাথে কার তুলনা করে?,1,politics
কোথায় জিয়া কোথায় রাস্তা রাস্তা গেও গেও করা কুকুরের মতো ওবায়দুল কাদের,1,politics
কাদের তোকে বলছি শোন তুই নিজে স্বীকার করতে চাস আওয়ামী লীগ ভিতরে দুষিত রক্ত আছে তোর নিজের জন্মের ঠিক নেই নেক্সটাইম কোন কথা বলার আগে আওয়ামী লীগকে নিয়ে বলবি বিএনপিকে নিয়ে এবং জামাত শিবিরকে নিয়ে না,1,politics
কুত্তালিগের কুত্তা রা একদিন শেষ হবে,1,politics
এই হিন্দু খানকি মাগীর ভোদা ফাটায় দেওয়া উচিত,1,politics
হাহা এগুলা মেয়ে নাকি পতিতালয়ে বেলুন দূর্ঘটনায় জন্ম নেওয়া মেয়ে,1,politics
কাদের মনে হয় ওর ভোদার বিতরে কাদেরর সোনা ডুকায়ছে এ জন্য তার কথা মুখে বাজে।তোর মারে চুদি তুই জিয়া পরিবাররে চোর বলিস।তোরে আমি পাইলে। ঘোড়া দিয়া ছোদায়তাম।বেশ্শা মাগি,1,politics
শিক্ষক মাদার চুদেরা হলে কুওা লীগের পা চাটা গেলাম খানকির বাচ্চার শিক্ষক চুদাই মাদার চুদেরা তোমাদের মত শিক্ষক কে ডাইরেক পাগলা কুওা দিয়া চুদাই তে মাগির বাচ্চার রা,1,politics
শেষ রক্ষা হবে নারে পাগলা ইনু,1,politics
মাগির পুলার আমানপুষ লীগ তোরা ত অমানুষ,1,politics
হিন্দু র বাচ্চা সে ত বলবে,1,politics
কুত্তা লীগ আর কত জনের জান কেরে নিবে একদিন তো মরতে হবে বুলে জাইসনা,1,politics
সেরা কাদের ওয়া কাদের চোরা কাদের,1,politics
অপু উকিলকে ওবায়দুল কাদের চোদে মজা দিছে তাই তার কথা বলে,1,politics
তুমি শালা আর কিছু পেলেনা তাইনা কত চাইছিলা যা দেয়নি বলেই উল্টা লেকচার ? চোর চোরের খবর জানে সেটাই স্বাভাবিক এসব লোক চুরি করে কোটি কোটি টাকার মালিক হলেও এদেরকে চোর বলেনা আত্নসাৎ বলে আর গরীবেরা পাওনা টাকার দাবি করলেও চুরিতে ভূষিত করেন। শাহেদ ভাই আমেরিকায় আছেন বলেই স্বৈরাচার সেহু হাচুনার নামে বুদনাম করছেন দেশে থাকলে আপনাকেও রাজাকার বলে কারাগারে রেখে দিতো যদি রাজাকারের প্রাপ্ত বয়স হয়নি আপনার হয়তো,1,politics
তিনটি মাগী নিয়ে অনুষ্ঠান। তোদের যৌবন যখন শেষ হয়ে যাবে তখন কুকুর ও তোদের দিকে তাকাবে না।,1,politics
এই শুয়ারের বাচচারাই তো দেশটাকে লুটে পুটে খাচ্ছে নইলে তুই তৃতীয় বিশ্বের একটি দেশ বাংলাদেশ সেই দেশের একজন মনত্রি যে দেশের ষাট ভাগ মানুষ এখনও দরির সীমার নীচে বাস করে আর তোর একটা ঘড়ির দাম দশ লাখ এ রকম বেশ কয়েকটা ঘড়ি যাহার মুল্য প্রায় এক কুটি টাকা এই টাকা অবশ্যই সত পথে আয়ের টাকা না সত পথে আয়ের টাকা হলে এত টাকা দিয়ে ঘড়ি কিনতোনা চুরি চামারির টাকা এদের নেংটা করে পাচা দিয়া গরম সিক ঢোকাইয়া দেওয়া,1,politics
এরে মাগি হাচিনার দালাল। কাদিরিয়া।আমর বাল,1,politics
আবাল চুদা মাজা ব্যাকা,1,politics
কুত্তালীগ শালা কুকুর কত দিন রাজত্ব করবে ফেরাউন ও টিকতে পারে নাই ইনশা আল্লাহ আল্লাহর গজব আসবে,1,politics
ছাএলীগনা ওরা কুত্তালীগ,1,politics
এই খানকির পুত রে মারি পালায় না কেন,1,politics
বাঞ্চদ সাংবাদিক কথা চাবাই অস্থি লাগে।,1,politics
মাগির ঘরের মাগির তাই হিন্দু ম,1,politics
এসব মাদারচোদের কাছে দেশ আমেরিকা মনে হয়। আফসোস আমরা সাধারন মানুষ সব কিছু থেকে বঞ্চিত।আজ আওয়ামীলীগ করতেছে কাল ক্ষমতা বিএনপি আসলে বিএনপি এরকম করবে। রাজনীতি আমাদের সাধারন মানুষের জন্য কেউ করে না সবাই আসে সবার পকেট ভারী করার জন্য। এসব মানুষের জন্য আল্লাহর তরফ থেকে একদিন গজব নেমে আসবে। আমার সোনার বাংলাটা হয়তো একদিন পুড়ে কয়লা হয়ে যাবে। তারপর আল্লাহর কাছে দোয়া করি যেন আমাদের বাংলাদেশ ভালো থাকে। অনেক ভালোবাসি প্রিয় দেশকে ❤❤🇧🇩,1,politics
ওবায়দুল আবাল,1,politics
হিজড়া জায়েদ,1,politics
কাউয়া কাদের লীগের ফাঁসি চাই,1,politics
চোদে কেও তোর খালেদারে,1,politics
আওয়ামীলিগ হল কুকুরের ছোদা জারুজ এই হিন্দু মহিলা কে পাইলে প্রকাশে ছোদলাম,1,politics
আওয়ামী বলদ,1,politics
আমি কোন রাজনৈতিক করিনা।কিন্তু কুত্তা লীগের মাইরে চুদি,1,politics
নাটাক চোদায়,1,politics
হ্যা তিনি খুব সৎ ও গরীব মাঝে মাঝে একবেলা খেয়ে দিন কাটায় । উনি খুব ভলো মানুষ তবে কিছু বেশ্যার বাচ্চা দেশটাকে ধংশের দিকে নিয়ে যাচ্ছেন !!!! তবে মাননীয় মন্ত্রী কিন্তু দুনম্বর লোক কিংবা জারজ টাইপের না,1,politics
কোথায় রাজরানী কোথায় চুদমারানী কাউয়া কাদের,1,politics
কাওয়া কদের,1,politics
কাউয়া কাদের।,1,politics
এইটা তো কুতা লিগের কাজ,1,politics
কুত্তালিগের সাথে কেউ পারবেনা কোথায় খালেদা আর কোথায় কাদের,1,politics
খালেদা জিয়া নিজেই একটা মাগী ছিলো,1,politics
অই সালা কাদির সালা চোরের মত কতা বলস কেন সালা আওয়ামিলীগের দালা,1,politics
আমলিগের খানকি মাগি তোর উপরে আল্লাহ্‌ গজব পড়ুক,1,politics
এই মাগি হচছে শেখ মজিবের চোদা,1,politics
হিন্দুর দাত দেকাজাকেন তার সুনা দেকাইনা কেন,1,politics
এই মাগি মরগ,1,politics
ওরা হাগুলীগ ওরা কুত্তা লীগ!ওরা হেলমেট লীগ।ওরা জারু লীগ।ওরা ডিম লীগ।ওরা মুজা লীগ।ওরা আওয়ামী লীগ।,1,politics
কে বলছে কাউয়া কাদেরের ব্যবসা নাই বাংলাদেশে কাউয়া কাদের এখন দ্বিতীয় সর্বোচ্চ ব্যবসায়ী প্রথম ব্যবসায়ী হচ্ছে মিউনাইট ভোটের প্রধানমন্ত্রী শেখ হাসিনা আর তাদের ব্যবসা হচ্ছে রাজনীতি এই আওয়ামী লুটেরাদের দেশে রাজনীতিই হচ্ছে সবচেয়ে বড় ব্যবসা।,1,politics
খালেদাজিয়া বাল ফালাইছে?,1,politics
জামাত শিবির রাজাকার আলবদর আল সাম নিপাত যাক ওরা সবাই পাকিস্তানি সেনাদের জারজ সন্তান জামাত শিবির রাজাকার আলবদর আল সাম মানে মাদার চোদ,1,politics
কই রাণী কই চুতমারাণী কই খালেদা আর কই কাওয়া কাদের।,1,politics
হায়রে কুত্তালিগ,1,politics
কুকুরের লেজের মতয় ছাএলিগ জতয় ছাইবে সোজা করতে কখনো সোজা হবেনা।,1,politics
ইসলামকে এই ইনুর মত কুকুরগুলো কিছুই করতে পারবে না। ইনু হাজার বছর থেকে বাংলাদেশকে রক্ষা করতে চায়। নাম্বার ওয়ান ছাগল।,1,politics
বিএনপি চুতমারানি কয় কি গাঞ্জা খাইয়া,1,politics
ইনুর নাম আজকে থেকে ইঁদুর ইঁদুর বললেই মনে করবেন ইনু এই ইঁদুর সুযোগ পেলে মাননীয় শেখ হাসিনা কে কামরিয়ে মারবে সিউর আমি মাননীয় প্রধানমন্ত্রী জননেত্রী দেশরত্ন শেখ হাসিনার কাছে আহ্বান জানাই এই ইঁদুর কে যেন আর কোন দিন মন্ত্রী না বানান কারণ ইঁদুরের স্থান মাথায় নয় গাথায়।,1,politics
তুই সালা মিথ্যাবাদী,1,politics
ওবাদুলকাদেরকাউয়ামাগিপুলা,1,politics
পাগলের বাচ্চা,1,politics
কুত্তা লিগ ঝারা করে সব কটা জারজ সন্তান,1,politics
কি বলেরে কোথায় মৌয়োর আর কোথায় কাওয়া ছি ছি ছি কিসের সাথে কিশের তুলনা নমো হারামজাদীরে বাশ দেয়না কেনো।,1,politics
আর এই মাগি যা বলেছে মাগিরে চোদছে কে ওর এখন বয়স কত হয়েছে একটু বলান,1,politics
যাদের জম্মের ঠিক নাই তারাই করবে ছাত্র লীগ। আর যেই শালারা এই সব কুকুরের জম্মদাতা তারা এক একটা কুকুর।,1,politics
দূর শাহেদ শালা আমিতো ঘড়িই পড়িনা।,1,politics
কাদের কাওয়া,1,politics
ওবায়দুল কাদের পোষা কুকুর বেগম জিয়া প্রধানমন্ত্রী তিনবারের শেখ হাসিনা মাথা খারাপ স্বামী নাই তো ওবায়দুল কাদের শেষ সম্বল তাইতো রাতে বাসায় যায় লোকের সামনে স্বামী হিসেবে পরিচয় দিতে লজ্জা পাচ্ছে,1,politics
আসলেই শালা বদমাইস একটা অরিজিনাল কাউয়া সত্যি কথাই বলছে,1,politics
ছাত্রলীগের গোসটি চুদি মাসটারের বেটিকে চুদি,1,politics
কুলাংগার কোথাকার কোন সভ্যতা নেই বদের হাড্ডি 😠,1,politics
মাগিরে গালে দিয়ে বরি দেওয়া উচিত তারেক কে দিয়ে চোদাতে হবে মাগি তো মালাউন চোদলে মাঝার ধরা চলে যেতো।,1,politics
শেখ মুজিবুর রহমান সহেব ভালো মানুয ছিলো মেডাম শেখ হাসিনা ও ভালো কিনতু বুজি না কিছু জারস আর খানকী আওয়ামীলীগ টারে বেইচা শেষ করলো আর অপু ওকিল কে সেফুদা কে দিয়ে চুদাই তে হবে মাগির কথায় তো খানকী দের মত ভালো হ আর কত চুদা দিবি,1,politics
আয় হালারপুত আওয়ামী লীগের পা চাটা গোলাম,1,politics
সে একটা বুকাচুদা,1,politics
বেগম জিয়া এর সাথে কাউয়া কাদের এর তুলনা!! শুনেই হাসি আসতেসে।🤣🤣😂,1,politics
বাইনচোদ তুমি থাকো আমেরিকায়। দেশের বালের খবর জানো তুমি। দেশে এখনো এক তৃতীয়াংশ লোক তিনবেলা খাবার পায় না।দেশে আসো জরিপ করে যাও। শালা তারেকের চামচা,1,politics
মাদারসোদ কথা ও বলতে পারে না আবার এমপি হোইছে 😠,1,politics
আমার ভোদার লীগ,1,politics
কাউয়া কাদের এর দিন শেষ!!!,1,politics
খালেদা জিয়া হল একটা চোর চোরের সর্দার চোরের সর্দার কিভাবে বড় হয় খালেদা জিয়ার বড় আবার সেই মেধা আছে নাকি আছে শুধু এতিমদের টাকা চুরি পেট্রোল বোমা মারামারির রাজাকারদের দিয়ে ভাঙচুর ও সন্ত্রাসী করা এ ছাড়া আর কি আছে খালেদা জিয়ার বড় চোরের তারেক সরদার আছে লন্ডন এ চুরি তো চুরি আবার সিনাজুরি শরম নাই তাদের যদি শরম থাকতো তাহলে বড় বড় কথা বলত না 👩‍🚒 👩‍🚒,1,politics
শালা কুত্তা লীগ জারজ খুনি হাসিনার দালাল পেটোয়া বাহিনী,1,politics
কাউয়া কাদেরের সাথে দেশ মাতা খালেদাজিয়ার সাথে তুলনা।পাগল,1,politics
ইনুর গলা সুকিয়ে জাচ্ছে ওকে একটু পানি খাওয়ান তোমাদের মত ছাগল মারকা রাজনিতিবিদদের সেক হাছিনা বেব্যহার করেছে টের পাপে কিছুদিন পর টেংকের ওপরে ওইঠা ফালাফালি করার ফল সামনে অপেক্ষেমান,1,politics
অপু একটা মাগি মাগির কথা শুনতেও খারাপ লাগে,1,politics
আওয়ামীলীগ হলো নাস্তিক বাচ্চা নাস্তিক উপু,1,politics
বাংলাদেশের খালেদার পরে য় খাংকি থাকলে সেটা হল ফারহানা রুমি,1,politics
অপু উকিল নাকি বেশ্যা বৃত্তি করতো!!?,1,politics
বেগম জিয়ার চাকরের চাকর নয় ঐ কাউয়া,1,politics
ওবাই দুল কাদের হলো ছাগোল চোর আরজে বলে সে হলো রাম ছাগোল।,1,politics
অপু মাগিকে পাছায় লাথ্যি মেরে বের করে দে,1,politics
মাদারচোদ তোরা আসলেই খারাপ কোটি কোটি টাকার মালিক লোকটা কোটি টাকার ঘড়ি হাতে দিতেই পারে এতোবেশি সমালোচনা কেনো তোদের মধ্যে তোরা কাদেরের কিছু করতে পারবি,1,politics
আমার লেওরা ঘটসে মাদার চোদ,1,politics
ওবায়েদুল কাদেরের নিষ্পাপ সততা দিয়ে খালেদাজিয়ার সাথে তুলনা করে 😀😀 খালেদাজিয়া দুইবার এ ভোট চুরি করে ক্ষমতায় এসেছে শিস্পাপ আওয়ামীলীগ করি করেছে 😀😀 চুতিয়ার বাচ্চা গুলা। দেশে কি মানুষ নাইরে?? পাবলিক কে কি এতই আবাল মনে করস? পাবলিক বুঝে না কিছু??,1,politics
মাগি শুধু বড়ো কথা বলে রুবি কে কচু দেওযার দরকার,1,politics
বোকাচোদা বাঙাল আমি নিজে দেখেছি আমার পরিচিত একজন বাংলাদেশী উনাদের বন্ধু কে একটি ঘড়ি উপহার দিয়েছেন লাখ টাকা দিয়ে। তুই খানকির মাগির পোলা পাছা চুলকানি কেন,1,politics
ভাই এই কুকুর লীগ কে মানুষ এত করে ওদের কোন ইজজত নেই এরা হাসিনার লেলিত কুকুর,1,politics
কুকুর কাদের কি করিতেছেন,1,politics
চোদাচুদির বই।।।,1,politics
অ সুদানির মাগি জিয়াউর রহমানের জুতার সমান হবিনা তুই মাগি জিয়াউর রহমান সত্যি কারে্র মানুষ ছিল তাই বাঙ্গাচুটকিজ আর ছিরা গেঞ্জি রেকে গিয়েছিল ৷ কিন্তু শেক মুজিব ত দেশের জনগণের টাকা লুট করে তার পরিবারের জন্য জমা করছিল তুদের কথাইত তুরা জে ডাকাতের দল এইটা বুজা যাছে,1,politics
আামার ধন ওবায়েূুল কাদের একটা পাঠা।,1,politics
এক পইসা বা পইসা সালা সব কিচু বুস্তে পারিস কিন্ত বুস্তে পারিস না তোই যে একটা রাজাকাই কুত্তার বাচ্চা,1,politics
যেখানে যায় হয় মেয়েদের বালপাক্নামি দেখলেই শরীর জলে!,1,politics
ছাত্রলীগ আর শিক্ষক সব শালারে পটিয়ে মারা জরুরি,1,politics
কোথায় কাউয়া কাদের আর কোথায় খালেদা জিয়া হাইস্যকর এইটা হাইস্যকর 😂😂,1,politics
একটা একটা কুত্তালীগ ধর ধইরা ধইরা বস্তায় ভর।,1,politics
তাকে আবার কে চুদলো 😋,1,politics
দুই দলিই চুর চুর চুর,1,politics
এই কুত্তার বাচ্চারা এই শুয়োরের বাচ্চারা জনগণের টাকা দিয়া লক্ষ টাকার ঘড়ি পড়ে এটা কি অর বাপের টাকা দেশটাকে ওরাই ডুবাইছে,1,politics
অপু উকিল এর পুটকির মধ্যে কেরোসিন ঢেলে দেওয়া উচিত,1,politics
না না শেষ কইরেন না শাঁকচুন্নি আরো কিছু বলতে চায়🤧🤧🤧🇧🇩🐛🐛,1,politics
ফকিন্নির পোলা মন্ত্রী হইছে ছোট বেলায় যে হাতে ঘড়ি দিতে পারেনি সেটা উসুল করে নিচ্ছে দৈনিক কোট পরিবর্তন সেটা আরেকদিন বলব,1,politics
বিএনপি হচ্চে জংগি পাকিস্তানি প্রোডাক্সসন,1,politics
কুকুর লীগের বিচার একদিন হবেই,1,politics
দোর চোরের বাচছারা,1,politics
আরে ভাই আপনি এখনো বোকার স্বর্গে বাস করছেন । বাংলাদেশ উন্নয়নের চোদনে ভেসে যাচ্ছে আমরা সকল দিক দিয়ে সফলতার চোদনে চোদনে ভেসে যাচ্ছি। আপনি কি জানেন না,1,politics
কুততা লীগ,1,politics
চুরের মার বড় গলা আওয়ামিলীগ এর দালাল মাগি?,1,politics
সালারে কাউয়া না কইলে কি বলবে সালায়তো সত্যিই কাউয়া রাজাকার দালাল নোয়াখালীর খাটাশ গরু চোর,1,politics
খানকিৱ বাচছা অপুঅকুল মাগিৱ বাচছা তোৱে আমাৱ সোনা টা তোৱ মোখে দিয়ে তাৱ পৱ আমিও বলবো তোৱে কিছু কৱি না,1,politics
সবগুলো ফকিন্নি র পোলা,1,politics
অপু উকিল আওয়ামীলীগের বড় পতিতা,1,politics
আওয়ামিলীগের ছাগি ছাগলের মত কি কয়,1,politics
অপু উকিলের শাউয়াদিয়া মানকছুদেওয়া হোক,1,politics
জারজলীগ তো সব সসন্ত্রাসী এদের কোনো বিচার হয়না,1,politics
খালেদা জিয়ার বালের সমান ও কাদের চোরা হতে পারবে না,1,politics
কাদিরের মা কে চুদি। এ সব টাকা গুলো জনগনের টাকা। মানুষের টাকা চুরি করে এসকরছে।।,1,politics
কুত্তার বাচ্ছা শিক্ষক না অন্য কিছু সালা হাসতেছে,1,politics
ইনু খাঁন কির পোলায় একটায় সুতিয়া,1,politics
ভাই বিএনপি তারেক জিয়ায় কিভাবে লন্ডনে থাকছেন কোনো কিছু করা ছাড়া সেটা বলতে লজ্জা লাগে? চুতিয়াগীরি ছাড়েন। আমি গ্রামের পোলা হইয়াও ম্যাকবুক কেম্নে ব্যবহার করি? আপনি যেহেতু নিম্ন জাতের মানুষ সেটারও একটা চুতিয়া লজিক দিবেন।,1,politics
জনাব কাউয়া কাদের পাগলা জাহিদ খান ও লুচ্চা ফারুক কে দেখা যাইতেছে,1,politics
খালেদার সাথে কাওয়া কাদেরের তুলনা কুথায় আগরতলা কুথায় পুটকির তলা???,1,politics
কাদের শুয়োরের বাচ্চার বিরুদ্ধে কোনো অভিযোগ দেখা যায় না কিন্তু সে মিডিয়ার চোখে চশমা দিয়ে ঘুরে বেড়ায় কিন্তু আজকে দেখে খুব ভালো লাগলো,1,politics
নুরা পাগলা আগাছা,1,politics
তুই জারজ সন্তানের জন্ম খানকির মাগি।,1,politics
বাইঞ্চোদ এর বাচ্ছা দেখে না তার জন্য রাস্তায় জ্যাম লেগে আছে,1,politics
ওরা কুলাঙ্গার ওদের জন্মে সমস্যা আছে দেশের সব্বোচ্চ বিদ্যাপীঠে বসে ওরা সন্ত্রাসী কর্মকান্ড চালায়? একজন ভিডির উপর হামলা চালায় এগুলো নর্দমায় কীটদের আক্রমন ছাড়া কিছুই নাহ্ মুজিব আজ বেঁচে থাকলে আত্নহত্যা করতো !! মুজিব এইরকম দেশ চায় নি!! ওরা মুজিবের আর্দশের কথা বলে তার আর্দশকে কলুষিত করছে,1,politics
পারলে কোনো মাদার চোদের বাচ্চা আয় দেখি কতটা হাছা কথা বলোছ,1,politics
কুত্তার চেয়েও খারাপ ছাত্র লিগ,1,politics
ওবায়দুল এর গুষ্টি চুদী শেখ হাসিনার গুষ্টি চুদী আওয়ামী লীগের গুষ্টি চুদী আমার মত যারা কুত্তালীগের চৌদ্দগুষ্টি রে চোদো তারা লাইক দাও,1,politics
মেয়ে গুলো এক নাম্বার ব্যাইশ্শা,1,politics
কার সাথে কার তুলনা?? ওবায়দুল কাদের আর আপোষহীন দেশনেত্রী বেগম খালেদাজিয়া?? বিষয়টা অত্যন্ত হাস্যকর যে এই তুলনা দিতে চাইছে উনার নারায়ণগঞ্জ ঘাটের নিষিদ্ধ পল্লিতে কন্ডম দুর্ঘটনায় জন্ম হইছে,1,politics
ছাগল চুতমারানি কয় কি কাউয়ার কথা,1,politics
কাওয়া কাদের বড মাগিবাজ ও দুর্নিবাজ ওকে জুতা মারুন,1,politics
সালা তুই একটা দালাল,1,politics
আমার মাতায় কাজ করেনা আপনারা এত লোগ এই মাছুদা গীগ কে পিছে পেলানো দর কার,1,politics
খানকির পোলারা এখন ভোটের সময় হয়েছে এখন কত কিছু করবে পারলে আপনার বাসার বাথরুম সাফ করবে ইলেকশনের পর একজন কো দেখা যাবে না,1,politics
কুওা কাদের বাইগা যা নইলে বাগনের সময় পাবিনা,1,politics
আমাকে একজুড়া চেড়া সেন্ডেল থাকলে দিবেন আমি অপু উকিল কে প্রথমে গুয়া মারবো পরে ওকে ইচা মত দুই গালে পেটাবো!!,1,politics
খানকির পোলা ছেলেদের হলে মেয়ে নিয়ে কেন ঢুকছিস,1,politics
ওবায়দুল কাদের হলো চোর আরএই চোরকে দেখে সিনেমার নায়ক নায়িকা সবাই দাড়িয়ে চোরকে সম্মান দিলেন ।,1,politics
কাউয়া কাদেরের আবার সুনাম। শালী কয় কি। এদের মত কুলাঙগার হাসিনার দালাল তোদের পাছা দিয়ে ডিম ঢুকানো দরকার।,1,politics
পশুর ও লজ্জা আছে এরা এই কমেন্ট গুলা পরে কি টু লজ্জা পায়না হায়রে পশুর দল,1,politics
কুত্তালীগ কাদেরকে কেউ শাসন করতে পারেনা,1,politics
ভিপি নূর সরকারের জম।বাঘের বাচ্চা। ছাত্রলীগ এর কুত্তা এক নুরুর বালের সমানও না।,1,politics
এই জানোয়ার লীগদের দেশ থেকে বের করা দরকার সালারা আসলেই জানোয়ারের চেয়েও নিকৃষ্ট।,1,politics
আমাদের দেশের কিছু লোক আছে ক্ষমতা পেয়ে বড় বড় কথা বলে সত্য কে মিথ্যা করে আর মিথ্যা কে সত্য বানাতে চায় অপু মাগি,1,politics
কুত্তালীগ দেশ টারে ধ্বংস করে দিচ্ছে,1,politics
বেগম জিয়ার বিরুদ্ধে এ পাগলি বলে কি ?,1,politics
কুত্তা লীগ মানদির পুতরা,1,politics
কাদেরের জাইঙ্গা টা নিয়া কথা ক সস্তা চোদা নির্বাচন এর আগে থাইকা বক বক চোদাইতাচোস ছি রতে পারস না কোন বা ল।,1,politics
ছাএ লিগের মারে চুদি,1,politics
লুঙ্গি লীগ হেলমেট লীগ ডিম লীগ জাইঙ্গা লীগ কুকুর লীগ বিড়াল লীগ চাপাতি লীগ খুনি লীগ ধর্ষক লীগ।।।।।,1,politics
এক মাতরো চুর খালেদা,1,politics
তুই কাদেরের সুদা খা সালি,1,politics
বাংলাদেশের আরেক নাম খা ল্যাদা!!! ওর শাওয়ায় জনের নুনু পেটের ভিতর এতিমের মাল পরনে পাতলা শাড়ি ঠোঁটে লিপিস্টিক ভ্রু প্লাক বছর বয়সে ও কাটনি ভিমরতি কেউ কি জাহান্নামি দেখতে চাও?খালেদার দিকে তাকাও। মহিলার উল্লেখ করার মত টা গুণ কেউ বলতে পারবা?? ভিডিওর বক্তাকে ও ফালু চাচা চুদছে,1,politics
ওবায়দুল কাদের তো লাইক একটি কাউয়া বেগম খালেদা জিয়া হচ্ছেন বাংলাদেশের কোটি মানুষের নেত্রী মাটি ও মানুষের নেত্রী তার সাথে কাউয়ার তুলনা চলে কিভাবে ?অপু উকিলের গালে জুতা মারি,1,politics
ওবাদুল কাদের একজন অবৈধ চোর বাটপার নিলজ্জ জনগনের শত্রু।,1,politics
তুই আসুদা,1,politics
হাছিনার নেতার অনেখেই মাগি বাজী,1,politics
কাওয়া কাদেরের নিকট এমন কিছু তথ্য আছে যার বিষয় একমাত্র শেখ হাসিনা জানে আর কাদিরা জানে যদি কাদিরা মরে যায় তাহলে শেখ হাসিনার পথের ভিখারি হতেহবে নতবা রাজত্ব হারাতে হবে তাই যেকোনো প্রকারে কাদিরাকে বাচাতে হবে,1,politics
চোরের বাচ্চা,1,politics
কাউয়া কাদের কার সাথে কার তুলনা। কোথায় তালের বিচি আর কোথায় ফেলের বিচি।।,1,politics
ছাএলীগ মানুষের জন্ম নয় ওরা সবগুলো জানোয়ারের জন্ম,1,politics
ইনু রাজাকার ওকে সরে রাখতে হবে আওমীলী কোন রাজাকারে থান হবে না,1,politics
মূর্খ নারী খালেদাজিয়া?,1,politics
মাদারি।,1,politics
ছাএ লীগের কুত্তা রা মানুষের বাচ্চা না,1,politics
এই চুর বাটপার আর মাগিবাজরা যদি সাধারণ মানুষদের মতো হালালভাবে কাজ করে খেতো তাইলে বুঝতো দুনিয়া কেমন আর কষ্ট কাকে বলে । মানূষের সেবার কথা বলে তাদের রক্ত চুষছে ।,1,politics
হোগা মাইরা দেশ চালায়,1,politics
কুক্কালিগ,1,politics
ইনু রাজাকা জংলি পালতু লোক তুই,1,politics
বেগম জিয়ার সাথে কাউয়ার তুলনা 😠😡😡 চোদমারানী অপু উকিল 😀😆😄😄😉🤓,1,politics
কাদের আমুলিগ মাগি র দালাল লুচচামি করে কাদের,1,politics
বাংলার জনগন বুকা চুদা,1,politics
শুয়োরের বাচ্চা ভিপি হইলে শপথ নেয়না কেন এটা দ্বিমুখী সাপ।,1,politics
কোথায় আগরতলা কোথায় পুটকিরতলা??? কই খালেদা জিয়া আর কই হিজ্রা কাদের?,1,politics
ছাগি ছাগলের মত কি কয়,1,politics
অপু একটা লেনটি মুনাপিক নাস্তিক,1,politics
আওয়ামীলীগ এখন পাগলা কুত্তার মত হয়ে গেছে,1,politics
খালেদা জিয়া চুর।,1,politics
আস্ত পাগল একা একা ঘেউঘেউ করেই যাচ্ছে আবার বলে সময় দিচ্ছে না।,1,politics
কার সাথে কার তুলনা কোথায় কাদের কোথায় বেগম জিয়া ছাগল কোথাগার,1,politics
ছাগলি বেগম!,1,politics
বাংলার কাউয়া,1,politics
নূরোর দেহি মাগীর অভাব নাই লপ হালুয়া,1,politics
কাওয়া কাদিরা পক কাদিরা,1,politics
ডিম না মাইর কুত্তার বাচ্চা জুতা মারা উচিত ছিলো।,1,politics
লজ্জা বলতে কিছু নাই। কুত্তা লীগ,1,politics
কাউয়া কাদের বাদ হবে তাহলে??,1,politics
হাচিনা চুর,1,politics
আরে চোরের বাচ্চা চোর লুচ্চা তুই চোরগো লুচ্চাগো ভিডিও দিছত এখানে তোর মারা আছে অপু কই,1,politics
কৈ হৈল কাওয়া কাদের আর কোথায় বারের প্রধানমন্ত্রী দেশনেত্রী বেগম খালেদা জিয়া,1,politics
কুত্তার বাচ্চা কার কাছ থেকে কি বুঝবে তারা কি মিথ্যা বলছে আবালটারে ধরে পিটালে ঠিক হবে।,1,politics
খালেদা জিয়া হলো দেশের নেতৃ তার সাথে কেনো কাউয়া কাদের??,1,politics
ঘাটে মাঠে এগুলো না করে বাসায় গিয়ে চা বানিয়ে খা পাগলের দল ছাগল গুলো।,1,politics
লুইচ্ছা কাউয়া চিঃ চিঃ,1,politics
জানুয়ার এর বাচ্চারা তোদের বিচার একদিন হবে ইনশাআল্লাহ।।,1,politics
মাতারি,1,politics
এই মাগি তো হিন্দু আর হিন্দুর বাচ্চারা যা বলে সব মিথ্যা বলে,1,politics
ছাগল চোদা আম্লিক,1,politics
প্রায় সব এম্পি মন্রিরাই চোর কাদের চোর বর মাপের চুর।,1,politics
আরে কুত্তা লিগের বাচ্চারা আগে কথা কি করে বলতে হই সেটা শিখ আর পর আসিস কথা বলতে তরা যে চোর সেটা তদের তুতলামি কথা তেই তরা বোঝিয়ে দিতেছত আমরা কি বলবো বল মনে রাখিস চোর কখনো পুলিশের সামনে তুতলামি ছারা কথা বলতে পারে না কারন মোখ দিয়ে সত্য কথা বের হইনা জোর করে বের করতে হই,1,politics
কাউয়া কাদের কা কা,1,politics
মেয়েরা এখানে যায় কেন। মেয়েরা তুদের কি বাচাবো ওরা তো নিজেকেই বাচাতে পারবেনা। ওরা মেয়ে নয় ওরা এক একটা ইবলিশ শয়তান। বেইস্যা মাগি। পুরুষের ধাক্কা খেতে ওদের মজা লাগে। সত্যি কারের মেয়ে হলে ঘর থেকে বের হতো না। সময় মতো ইস্কুলে যেতো আর সময় মতো ফিরে আসতো এবং হিজাব পরে। রাজনৈতিক কাজ এদের জন্য নয়। দেশে এতো ইভটিজিং কেন হচ্ছে। কারন মেয়েরা চায়। ইভটিজিং,1,politics
দেশের নম্বর জঙ্গি ছাত্রলীগ,1,politics
কুত্তা লীগ এর ই লাইসেন্স নাই ওরা আবার জনগণের লাইসেন্স চেক করে তো দের নাটক জাতী বোঝেন,1,politics
ওবায়দুল কাদেরের সুনাম হাহাহাহাহাহাহ বালের সুনাম কাউয়া,1,politics
রাইট হাসিনা নাস্তিক ভোট চুর,1,politics
কোয়া কাদিরা শালায় বাংলাদেশের গরীবের পেটে লাথ্থি মারছে রেয়াই পাইবেনা কোয়া কাদিরা বাংলার মাটিতে রেয়াই পাবেনা,1,politics
ছাত্রলীগ একটা গুন্ডা সংস্থা,1,politics
তুই মাতারি কিবলচ,1,politics
শালার কাউয়া,1,politics
কুত্তালীগেল ধবংস ছাই,1,politics
সব টি হাসিনা পালা কুকুর,1,politics
নূরুকে ডিম কেন মারা হল ? ওকে তো গু মারা দরকার ছিল।,1,politics
আওবামালীগ এখন বেশ্যার ভাতের হোটেল প্রত্যেক মাগিদের মাথায় টিপ আছে যেটা বেশ্যার চিহ্ন,1,politics
কুত্তালিগ এর বাচ্চারা খমতা দেখিয়ে আজ আমার দুকান থিকা জুর করে নিয়ে গেছে এর আগে ও অনেক গোলা নিছে আমারা সাধারণ মানুষ বিপদের মুখে আছি,1,politics
বুঝা যাচ্ছে কুত্তা লিগ সব পারে ।।।।কার সাথে নিয়ে কার তুলনা করে মাগি ।।।ওবায়দুল্লার আরেক মাগি ।।সাবধান হয়ে যা,1,politics
যতো নাস্তিক দালাল টাউট বাটপার চুর ডাকাত!! সব আওয়ামীলীগ।,1,politics
কাউয়া কাদের,1,politics
বাংলাদেশ আওয়ামী লীগে ওবায়দুল কাদেরের মতো বাটপার আর একটা খুজে পাওয়া যাবেনা । সরক ও যোগাযোগ এই সরকারের সবচাইতে ব্যার্থ মন্ত্রনালয় । তারপরও বাটপার কাদেরের কোন লজ্জা নাই ।,1,politics
কাদেরের মারে চোদি,1,politics
গাঁজা নুরু,1,politics
কুকুরকে চেষ্টা করলে মানুষ বানানো সম্ভব কিন্তু ছাত্রলীগ কখনো মানুষ হবেনা,1,politics
ছাএলিকের মারে চোদি মাগির হোলা,1,politics
বি এন পি মানে জারজ দল,1,politics
কাওয়া কাদের খালেদা জিয়ার শরীরের উচ্ছিষ্ট দ্রব্যের সমতুল্যও নয় । অপু উকিলের যদি তাকে বেশী পছন্দ হয় তাহলে তো পথ খোলাই আছে তাইনা ।,1,politics
হাসিনার রিপ্রেজেনটেটিভ তো কথাই বলতে পারে না কাদেরের রন্ধ্রে তার সোনা রয়েছে,1,politics
ওকায়েতুল পাদেন কাউয়া হিগার মার হাউয়া,1,politics
পাবলিক বিশ্ববিদ্যালয় আমার পুটকির বাল।,1,politics
কথায় কাউয়া কাদের কথায় খালেদা জিয়া,1,politics
দেশে একমাত্র ওবাইদুল কাদেরি আছে যার কাজে ভুলের সংখ্যা সবচেয়ে কম এবং নিখুত তোরা মাগিরপোলারা যারা পুরা ভিডিও না দেখে শুধু লেখা দেখে কমেন্ট করচোস তোর এলাকার রাস্তা কি তোগো বোউরা চুইদা করছে,1,politics
এখানে অপু কোথায়? হালা মাদারচুত,1,politics
জারা হামলা করছে তাদের কে জানোয়ার চোদা খায় জন্ম হয়ছে,1,politics
কোথায় শেখ শাদি আর কোথায় বোরকির লাদি খালেদা জিয়ার মুতের সমান ও তো হতে পারবে না ওবায়দুল কাদের।,1,politics
কোথায় কাউয়া কাদের আর কোথায় খালেদা জিয়া। শালারা কি কয় না কয় লজ্জা থাকা দরকার।,1,politics
স্যার মাদারচোদের বাচ্চারে থাপড়াই চোবরাই গালের দাঁত ফালাই দেওয়া উচিত শালা দালাল ছাত্রলীগের,1,politics
ছাত্রদেরকে মাইরা এখন নাটক চুদাও।,1,politics
বোকা চোদারা কিসের সাথে কি মিলায়,1,politics
এতো একটা হিজরা বলদ।,1,politics
কুত্তার লেজ যেমন কখনো সোজা হয় না তেমনি ছাত্রলীগ কুত্তার বাচ্ছারা কোন দিন ভাল হবে না।,1,politics
ড়িম লিগ হলোকুত্তা লিগ,1,politics
লিগ মানে খানকি মাগির জারজ সন্তান,1,politics
কুতালিগ এদের জন্মের দোস আছে দেশ নেএি সাতে তাদের তুলনা না দিয়ে তার জুতার সাতে তুলনা দেওয়া দরকার ভারতীয় দালাল খুনি হাসিনাকে,1,politics
ওপু পাগল আর চামচা মি করে,1,politics
আওয়ামীলীগ খানকির মেয়ে মাদার চোদ,1,politics
মাগিবাজ কাদেরের সাথে খালেদা জিয়ার তুলনা।,1,politics
আমার বালের লীগ সালারা।আর ঐটা আমার বালের টিচার,1,politics
ওবাইদুল কাদের শালায়তো মরে না,1,politics
ছাএদল মানে কুতার দল,1,politics
তোর বাবা জংগি চুতিয়া,1,politics
কাওয়া কাদের কা কা কা কক কক শালা একটা চুতমারানি ভোট চোর,1,politics
এইটা ভাল হইচে নুর সালা তুই পাগল,1,politics
খালেদা জিয়ার সাতে কাউয়া কাদেরর তুলুনা হয়না,1,politics
অপু উকিল এর বোধা দিয়া যদি আইক্কা ওয়ালা বাঁশ ডোকাইয়া চৌরাস্তার মোরে বসানো উচিত।,1,politics
যেমন দল তেমন সেই দলের কাওয়া নেতা পতিতার দল,1,politics
কুত্তালীগ মার্কা জানোয়ারের বাচ্চায় এগুলো কি বলে,1,politics
ছাত্র লীগ মাদারচুদ,1,politics
বোদার মধ্যে অপুকে কিছু বলছে বোকা চোদা,1,politics
ওবায়দুল কাদের চোর না খালেদা তারেক চোর,1,politics
এই জারজ লিগ কে যে জরমো দিছে তারা নিচ সনদেহে পতিতার বাচচা,1,politics
দলবাজি শিক্ষক প্রসাশন মাদার চৌদ্দ,1,politics
মাগি মিত্যা বাদি ওরে কুত্তা দে চুদা কাদের এর মাগি,1,politics
কুকুর লীগ দের সাথে কেনো টক সতে আসেন,1,politics
রাজনৈতিক নেতাদের প্রশ্রয়ে ছাত্রলীগরা আজ সন্ত্রাসী লীগে পরিণত হয়েছে। আর ঢা বির কতিপয় শিক্ষকরা হল সত্যি কারের শুয়োরের বাচ্চা। এদেরকে কুকুর দিয়ে মারা উচিত।,1,politics
খানকী অপু উকিল তোদের দুর্নীতি তোদের মধ্য রাতের ভোটের প্রধন মন্ত্রী সহ সকলকে সারা বিশ্ববাসি থুতু দেয় 🤫🤫🤫🤫🤫🤫🤫🤫🤫🤫,1,politics
কই রাজ রাণি আর কই কাদের চাকরানি,1,politics
সুয়রের বাচ্চা ডাকাত লে লে করে কথা কয়,1,politics
ওবাদুল কাদের একটা বলদ এই গরমের মধ্য কি এটা মুটাকুট গায়দিছে বলদ,1,politics
বাংলাদেশের জঙ্গি সংঘটন হলো কুত্তালীগ,1,politics
শালা নূরা ভিপি অইছে,1,politics
শয়তান এর কন্ডম ফাটা জারজ এর সন্তান এগুলি,1,politics
খানকি অপু বিশ্বাস।,1,politics
আওয়ামীলীগ মানেই জারজ লীগ,1,politics
হুম প্রশাসন এখন বাল ফালায় এগিয়ে যাও নুরু,1,politics
অপু তোর মুকে মুতি,1,politics
ভাত পঁচে গেলে মদ হয়।মদ খেলে মানুষ বদ হয়। বদ পঁচে গেলে নাস্তিক হয়।নাস্তিক পচে গেলে মুশরিক হয়। আর মুশরিক পচে গেলে জারজ হয়।আর জারজ পচে গেলে আওয়ামীলিগ হয় !!!😂😂😜😜,1,politics
শাউয়াপাগল কাউয়া একটা। ভায়াগ্রার ওভারডোজে মরতে নিসিল তাও হালার লুচ্চামি কমেনা!,1,politics
ওবায়দুল কাদির একটা জারঝ সন্তান কারন ওবায়দুল কাদিরের জন্মের টিক নায়,1,politics
কই রাজ রানি খালেদাজিয়া কই কুকুরে বাঁচা কাদের বাট ফার,1,politics
হিন্দু মাগির কথায় কোন যুক্তি নাই মাগি একটা বলদ,1,politics
খানকির বাচ্চা কারে কইলাম বুজ্জা লন।,1,politics
খানকির পোলা এইসব ছাড়া কি তোর কাজ নাই না থাকলে ওবায়দুল কাদেরের ময়লা পরিস্কার কর।,1,politics
কাউয়া কাদেরকে নিয়ে একটি ভিডিও করার ইচ্ছা আছে। যাতে দেখাবো কাউয়া কিভাবে বক হয়ে যায়। সাব করুন। দেখতে পাবেন।,1,politics
কাউয়া কাদের কত বড় মাগীখোর সেই তার ভিডিও ও পিক দেখলে বুঝা যায় লুচ্চা কাদের টা ঘন্টা বেশ্যাদের সাথে থাকে সেই মেয়েদের কোন চরিএ নেই,1,politics
পাগলে কিনা কয় ছাগলে কিনা খায় খালেদা জিয়ার পায়ের নিচে যে বালি থাকে ওবায়দুল কাদেরের সে দামটাও নেই,1,politics
চোরের বাচ্চা চোর,1,politics
শালার কুওালীগরে ভাই কুওা লীগ বিখাউজ,1,politics
অা লীগের মাগি তোরে জুতাপেটা করবো,1,politics
অপুকে লেংটা করে মার তাহলে মিথ্যা কথা বলা বাদ দেবে।।,1,politics
হা হা হা হা এটা হাস্যকার 😂🤣🤣 খালেদা চোর পাকিস্তানি জারজ ওবায়দুল কাদের পার কাছে যেতে পারবেনা খালেদা,1,politics
অপুকে পতিতার মতো লাগে খানকি মাগি,1,politics
ওভাদুলকাদের চুর,1,politics
শালার পুত শালা রা আগুন জ্বালো আগুন জ্বালো মিছিল শুধু আগুন কই ? ছাত্রলীগ যদি মারতে পারে তোমরা কার বাল ফালাও,1,politics
এই সালাও কুত্তালীগ করে জারজ,1,politics
ভিপি তোর পাছার ভিতর জাবে।সালি রববানি ভাইর ছিট দখল করতে চাও।আশা বাশা হবে।,1,politics
কুত্তালীগের চুষা কামলা গুলা ভিডিওতে দিয়েছে,1,politics
অপু একটা পতিতা,1,politics
হাস্যকর কথা বলে গেলেন কুত্তা লীগ এর কমি,1,politics
বর্তমান আওয়ামী লীগ একটা মাতালদের দল,1,politics
উবাদুল তু কাউয়া একটা,1,politics
খুনী লীগ ধংস হোক,1,politics
আমি আজ সাধারন ছাএদের বলতে ছাই তোমরা ছাএলীগ নামক কুওাদের গুলি করে আলাদা আলাদা করে ফায়ার করে মেরে ফেলো কারন এরাতো মানুষ না এরা কুওা সো কুওাদের মারলে কোন বিচার নেই,1,politics
খান্কির পোলার বিচার আল্লাহ করবে,1,politics
আওয়ামী এর কুত্তা জারোজ মেয়েরা এই সব টকশো এর কমেন্ট গুলা দেকতে পাই না,1,politics
যেখানেই সমস্যার সৃস্টি সেখানেই কুত্তালিগ কুত্তালিগ মানেই সমস্যা,1,politics
ইউটিউবার এর মাইরে বাপ খানকির পোলার কথার সাথে কাজের মিল নাই ওবায়দুল কাদের কি ধরা খাইছে সেটা তো দেখালি না খানকির পোলা,1,politics
খানকি মাগি,1,politics
ওবায়দুল কাদের সালা একটা কুকুর,1,politics
ছাএলিগ মানি পতিতার বাচ্চা আওমিলিগ মানি কুকুরের বাচ্চা,1,politics
কোথায় আকাশ আর কোথায় পাতাল। কাউয়া কাদের তো সমান্য বেগম জিয়ার সাথে মুজিম কাক্কুর তুলনা ও হবে না গনতন্ত্রের মা হলেন বেগম জিয়া,1,politics
মুয়েরের সাথে কাউয়ার তুলনা 😁😁😁,1,politics
বাল উপযোগী সিদ্ধান্ত হাগিনা নেবে।।,1,politics
কাউয়া কাদের ওয়ান ইলেভেনের কথা মনে হয় ভুলে গেছে,1,politics
ও কি বোকাচোদা নিজের পাওয়ার দেখাচ্ছে।এত লোক জমায়েত হয়েগেছে গাড়ি একটাও যেতে পারছেনা এত কি বড় বাহাদুর মনে করে।,1,politics
নুরার রেনডি দল,1,politics
বাঙলাদেশে যদি একজন কুলাঙার থাকে সেটা হলো এই কাফের ইনু।।।,1,politics
ছাত্রলীগ কুত্তালীগ এর মধ্যে পার্থক্য কি ?,1,politics
কাদের হালা নুয়াখাইল্লা।,1,politics
দেশটা ধংসের দিকে নিয়ে যাচ্ছে কুত্তালীগ,1,politics
কাদিরা।পাগলা।একটা। লুচ্চা,1,politics
পাগল ছাগল,1,politics
শালা গুলাকে রাস্তাই ফালাইয়া মারা দরকার,1,politics
কুত্তার বাচ্চারা ফেরাউন বাচে নাই তোরাও বাচবি না।,1,politics
হিন্দু মাগি,1,politics
মিথ্যুক শিক্ষক হালারপুত,1,politics
কুত্তালীগের হামলার শিকার সবাই,1,politics
কথাই রাজ রানী আর কথাই অবায়দুল ফকিরনীর বাচ্চা,1,politics
টিছার নামের -- মাদারচোদ,1,politics
অপু ওকিলরে রেডি থাকিচ তোর বোদার বিতোরে মরিচ গুডা করে দেওয়া হবে তারেক এবং খালেদা জিয়ার নাম নিছো অযু করছো খানকিমাগির জি তোরাতো সব জারোজ তোগো বাপ কয়জন কয়তে পারবিনা তোরে ঘোড়া দিয়েতোরে চুদামো,1,politics
কুত্তা লিগ এখন ডিজিটাল হইচে এখন হইচে আন্ডা লিগ,1,politics
নিচ্ছয় কুত্তা কাদের বড় হবে,1,politics
একানে সব সয়তানের দল,1,politics
ওবায়দুল কাদের হল লুচ্চা,1,politics
আওয়ামীলীগ চুদিনা কাওয়া হালারা,1,politics
মাগি ফারজানা,1,politics
কোথায় কাউয়া কাদের অার কোথায় বাংলাদেশের সাবেক প্রধানমএি বেগম খালেদা জিয়া!,1,politics
কাউয়া কাদের কে শরাবে হচ্ছে নাসিম ভাই🤗🤗 এজন্য ইদানিং নাসিম ভাই খুব পটপট কথা বলছে 🤗🤗🤗 সবই বুঝি 🤗🤗🤗,1,politics
অপু চুদা খাভে,1,politics
বোদা কেষ্ট,1,politics
কাউয়া কাদেরকে সরিয়ে দেয়া উচিত।,1,politics
কোথায় কাউয়া কাদের আর কোথায় সাবেক প্রধানমন্ত্রী বেগম জিয়া রাজার সাথে তুলনা কখনই হয়না,1,politics
জারুজ সন্তান কুকুরের ছোদা আওয়ামী লিগ,1,politics
আওয়ামীলীগের খানকি রে বাশ দে। চুদানির বড় বড় কথা। চুদানি বলতাছে ভোট চুরির কথা। লজ্জা থাকলে বড় গলায় কথা বলতে পারতো না।,1,politics
হেডা জিয়া,1,politics
তরা আওয়ামীলিগে ছোট ছোট ভাইরাস ইনুর কথার মধ্যে জংগী হাসিনা ইদুরের সভাব পাওয়া গেছে,1,politics
এটাও কুকুরের বাচ্চা এই স্যর,1,politics
দেশে এমন কেউ না যেই এইসব নাটক ডার্মা বন্ধ করবে এবং কুত্তা লিগ আওয়ামিলীগ এবং বিএনপি এঁদের যদি রাজনৈতিক থেকে বন্ধ করে দেশে নতুন কেউ দেশের আইন ব্যবস্তা নতুন করে হাজাক এবং তৈরি করুক এবং কুত্তা লিগ আওয়ামিলীগ এবং বিএনপি এঁদের রাজনৈতিক থেকে একবারের জন্য বন্ধ করা হোক!! আর বুঝিনা এইসব নাস্তিক কুলাঙ্গার শেখহাসিনা খালেদা মরেনা কেন এঁদের মৃত্যু হয়না কেন আজরাইল এসে এদের জান কবজ করেনা কেন এরা তো % জাহান্নামে যেতে পাড়ে এবং যাবেও এঁদের দুই কুলাঙ্গার কুত্তীর মা বোন বাবা ভাই কেউ নিরাপত্তা পাইনা সবসময় ভয় থাকতে হয় চলাফেরা করতে হয়!! আল্লাহ তুমি শেখহাসিনা খালেদা উপর গুজব দাও না কেন কবে শুনবো শেখহাসিনা খালেদা আর নেই জাহান্নামে গেছে বাহ যাবে নাস্তিক কুলাঙ্গার শেখহাসিনা খালেদা মৃত্যু দাও তাহলে দেশ আবার নতুন করে গড়ে উঠবে ইনশাআল্লাহ!!!,1,politics
কাদের একটা কাওয়া। তাই ময়ূরের পাখা লাগিয়ে ময়ূর হতে চায়। সালা কুত্তার বাচ্চা কাওয়া।,1,politics
তোরে ও তোর মাকে চুদিবো কতো লাগবে,1,politics
সালা নোয়াখাইল্লা কাউয়া,1,politics
শালারপুত মিথ্যা কথা বলোস কেন বিপি নুর তুই যেগুলো অভিনয় করতাসোস সেটা বাংলাদেশের মানুষ জানে তুই তো একজন জমাট শিবির তুই একজন বাংলাদেশের শত্রু সব গঠনা তুই করতাসোস তুই এক জমজমাট শিবিরের লোক,1,politics
এই ছাগলের বাচ্চাটা কে ওরে কেন একানে আনা হলো,1,politics
পাগলের বাল খালেদাজিয়ার সাতে হাসিনা তুলনাও চলেনা কারন বাংলাদেশের লোক ও হাসিনাকে চায়না।।।,1,politics
ভিপি নূর ভাইকে জে গায়ে হাত তুলেছে সে হলো রাজাকার এবং দেশের সক্রু আর জারজ সন্তান,1,politics
জানোয়ার লীগ একদিন তোদের কে কুকুরের মতো পিঠাইবে বাংলাদেশের জনগন,1,politics
মালায়ন বাচায় কি কয়,1,politics
কে করবে কত্তালীগের বিচার,1,politics
মাগি তোরে ঠিইক সতন বাগুন দিলে ভালও হইত তোর ব্যবহার ভালওনা,1,politics
জনগণের টাকা নিয়ে গৌরব করিচ শালা? মরলে বুঝবি।,1,politics
এই ডান্ডি রেনডির বাচ্চা কে কুততা দিয়ে চুদার দরকার,1,politics
মাগি তোর কথা হয়ে না,1,politics
বুড়ি তুই শেকহাচিনার দালাল,1,politics
কাদের কাওয়া নামে পরিচিত,1,politics
আমাদের বেশা মাগি,1,politics
দেশনেত্রী বেগম খালেদা জিয়া হচ্ছেন দেশের মা ওবায়দুল কাদের গরু চোর,1,politics
কুত্তালীগ কাংখির পোলারা,1,politics
এই মালাউনের বাচ্চা ব্যাংকের কোটি টাকা কই গেল?,1,politics
সব গোয়া তারেক মারছে তোর মাকেও তারেক করছে মাদার চোদ মাগি,1,politics
বাংলাদেশের তিন তিনবারের প্রধানমন্ত্রী দেশনেত্রী বেগম খালেদা জিয়া তার সাথে ওই চোর ওবায়দুল কাদের এর তুলনা দেওয়া ঠিক বলে আমি মনে করি না বাংলাদেশের এই শেখ হাসিনা সরকার আসার পরে দেশে ধর্ষণ প্রতি প্রতিদিন ধর্ষণ আসলে শেখ হাসিনা সরকারের দোষ না দোষ হলো শেখ হাসিনা সরকারের যেগুলো নেতা আছে সেই নেতাদের আবার কিছু কুত্তা সেই কুত্তারা এগুলা করে শেখ হাসিনার দোষ নয় শেখ হাসিনা একটা মানুষ কি করবে সে শেখ হাসিনার দোষ নয় এটা হল তার কুত্তা গুলা আছে এই কুত্তা গুলার দোষ,1,politics
ও মাগো আননেরা হেতেরে বলদ কইয়েন না 🤫 হেতে মোগো দেশের সেতু মন্ত্রী 😯🙄 বলদ হলে মন্ত্রী হলো কেমনে??,1,politics
এই কুত্তালিগের বাচ্চা দের উপর আল্লাহর গজব পড়ুক,1,politics
ডাইটা মাগী চামচামী আর কত করবি একদিন ইনডিয়ানেরাও তোদের বাচাতে পারবেনা।নির্লজ্জ বেলাহেজ ভোটচোর,1,politics
যে লোকটা অবাইদুল কাদেরের সাথে বেগম জিয়াকে তুলুনা করবে সে মানুষ না সে একটা গরু,1,politics
তোর মারে চোদার কথা কেউ ভুলে নাই,1,politics
মাঝে মাঝে নায়িকাদের নিয়ে মিটিং করে আর দেখে কার পাছা বড় কার দুধ বড় আর যাকে পছন্দ হয় তাকে বিছানায় ডাকে এটা হলো আমাদের দেশ গোড়ায় গন্ড গোল,1,politics
বেইজ্জতি বেশরম বেইমানি শয়তানি হার্মাদি এগুলা থেকে শয়তান অব্যাহতি নিয়ে নিয়েছে !,1,politics
ওবাদুলকাদের একটা উলা বিড়াল।,1,politics
মাগীর দেশ আমাদের ই বাংলাদেশ,1,politics
ভিপি নূর নিজেকে বড় নেতা ভাবছেন। সালার হোগার ভিতরে ডিম ঢুকিয়ে দিলে ভালো হবে।,1,politics
সাওর মাগি একবার পড়ে দেখ তোর সাও কিভাবে ফাটায়,1,politics
দল ক্ষমতায় না থাকলে পুটকি মারা দিয়ে ভাত পেতনা মাদারচোদ ওবায়দুল কাদের আবার ঘরি চুদায় কামলার বাচ্চায়,1,politics
নাস্তিক মুরগি চুর এইখানে কি করে,1,politics
কাওয়া কাদের অনেক বুদ্ধি মান লোক তাই সে আগে থেকেই জানে যে আমার ভবিষ্যতে এই ট্রাফিকের কাজ করা লাগবে তাই এখন থেকে প্রশিক্ষণ নিচ্ছে,1,politics
অপু উকিল তুই তো ভোট চোর তোর মুখে লাথি মারী ।,1,politics
কুত্তা লীগ মানে চোর কুকুর লীগের মায়রে চুদি,1,politics
হিন্দু মাদারি মাগি তোর মুখ সামলা পতিতায়ের কীট খাংকি,1,politics
আমিলীগের মারে চুদি,1,politics
এ কুত্তার বাচ্চা তো চোর হালারে জুতা দিয়ে পিঠা,1,politics
আমি মেঘনা ব্রীজ দেখেছি । রাঙামাটির ঝুলন্ত ব্রীজ দেখেছি। ময়ূরীর গরম মশলা দেখেছি। হলিপুর ভিডিও দেখেছি হাতিপুর এডিটিং ছবি দেখেছি। হিরো আলমের আবাল মার্কা ছবি দেখেছি নাতাশা সানি লিওন মিয়া খলিফার ভিডিও দেখেছি। কিন্তু বিশ্বাস করেন ভাই আপনার মত বাইন চোদ পোষ্ঠকারী জীবনে ও দেখেনি।।😷,1,politics
আমার বালের আওমিলিগ দালাল মাদার ছুদ কাউয়া মন্ত্রীর ওবায়দুল কাদের,1,politics
এই অপু খানকি মাগি তোরহাছিনা ও জয় কতকুটি চোর বল,1,politics
কাদের নায়িকা গো রে চুদে,1,politics
ভাত পঁচে গেলে মদ হয়।মদ খেলে মানুষ বদ হয়। বদ পঁচে গেলে নাস্তিক হয়।নাস্তিক পচে গেলে মুশরিক হয়। আর মুশরিক পচে গেলে জারজ হয়।আর জারজ পচে গেলে আওয়ামীলিগ হয় !!!,1,politics
মাদের চোদ তুই একটা সত্যি কারের দালাল,1,politics
যতদামি ঘড়িই পরুকনাকেন কাউয়া কাউয়াই থাকবো।শুধু কাউয়া না লুইচ্চা কাউয়া ।নোয়াখালির কলঙ্ক ।,1,politics
হিন্দু মহিলা কে জুতো মালা দিয়ে স্টিজ থেকে বের করে দাও,1,politics
এই স্যার একটা কুত্তা লীগ,1,politics
বিশেষ অনুরোধ করছি সময় টিভিকে অপু উকিল কে সেপুদার কাছে পাটানো হোক আমি শিউর তার জন্ম কোন এক পতিতালয়ে হয়েছে না হয় কনডম পুটো হয়ে জন্ম হয়েছে। তর মাগির ঘরের মাগি,1,politics
বাংলাদেশের মানুষের কাছে গনতন্ত্রের উজ্জ্বল দৃষ্টান্ত খালেদা জিয়া।কাউয়া কাদের চোর।,1,politics
খানকির পোলায় মরণের দুয়ার থেকে ফিরে আসছে। এখনও কোন পরিবর্তন নাই। সেই রাম রাম,1,politics
কোথায় ওবায়দুল কাদের ছাগল খালেদা জিয়া হলো মানুষ এইটুই মনে রাখবেন,1,politics
আরো কতকিছু শোনব কুত্তা লীগ হেলমেট লীগ গুন্ডা লীগ জারস কুলাংগার ও শেষমেশ ডিম লীগ। বাহ বাহ এটাই বর্তমান সরকারের ডিজিটাল শিক্ষাঙ্গনের ডিজিটাল হাল,1,politics
ওপু উকিল আপনিযে একটা খানকি মাগি এটা বুঝা যাচ্ছে আর কার সাথে কার তুলনা করেন আপনি কুথায় কাউয়া কুথায় বেগম জিয়া।,1,politics
তোমাদের পুটকি দিয়া জনগন ডিম দেবে ডিম রেডি আছে,1,politics
মিডিয়া নাম্বার মাদার চোঁধ,1,politics
সালা নকি পাগল ওবাদুলকাদের জানজোট বানাচে তার সাজা কিহয়র ওচিত আপনারা জানাবেন সালা কুতালীগ,1,politics
অপু উকিল তোর বোদার বিতর কন্সিওয়ালা বাঁশ ডুকানো হবে,1,politics
হাসিনা মাগির ফাঁসি চাই ✊✊,1,politics
হাছিনার কুওারা ছাএলিগ,1,politics
কোথায় খালেদা জিয়া আর কোথায় কাউয়া কাদের,1,politics
কুত্তার বাচ্চা ছাএলিগের মারছে,1,politics
কুকুর লিক মুক্ত বাংলাদেশ চাই,1,politics
লীগ সেখ হাসিনার আমি চুদি,1,politics
শেখ হাছিনার দালাল আওয়ামী কুকুর বাচ্চা কুকুর ওসি,1,politics
কাউয়া কাদের আমার সোনার মাতা,1,politics
অপু উকিল একটা লাইসেন্স করা নটি ওরে শুদু জুতা মারার দরকার,1,politics
আওয়ামীলীগের নামে যেই মাদারচোদ যে খারাপ কথা কইবো তার খবর আছে,1,politics
তোর বাবার দেশ নাকি মাদারচোদ গল্প সাজাও ছাব্বিশে কি আসবে মাদারি,1,politics
চুদির ভাই গ কি জিনে কুতকুতানাকি।,1,politics
এই কুত্তার বাচ্চারা কেউ লেখাপড়া করতে আসেনি । ওরা শুধু মারামারি করতে এসেছে । ঢাবির ছাত্র ছাত্রীদের আসলে মেধাবী বললে ভুল হবে । এরা সাধারণ শিক্ষার্থীর চেয়েও কম মেধাবী। কারণ এরা শিক্ষার্থীর পর্যায়ে পড়ে না।,1,politics
হিন্দু মাগীকে কুত্তা দিয়ে চুদাতে হবে,1,politics
অপুর মুখে মুইত্তা দিলাম 👯,1,politics
তোর মায়ের মাং খান্কি মাগির পুত,1,politics
কোথায় খালেদা জিয়া হাতি কাওয়া কাদের শাতে ছাগলের তুলনা,1,politics
খালেদাত চুর,1,politics
রুমেন ফারহানা খানকী মাগি জারক ওবায়দুল কাদের মহান নেতা খালেদা জিয়া খান কির বাচ্ছা জারোক,1,politics
কুত্তা লীগ,1,politics
কোথায় কাউয়া কাদের আর কোথায় খালেদা জিয়া। কিসের সাথে কি পান্তা ভাতে ঘি।। হা হা হা,1,politics
ছাত্রলীগের গুষ্ঠি চুদি। যুদ্ধ শুরু করতে হবে ছাত্রলীগ বিদায় হবে। শালার ছাত্রলীগের অধিকাংশ মানুষ কাফের কারণ তারা নামায পড়ে না দাড়ি সহ্য করতে পারে না। কাফের ছাত্রলীগে কেউ যোগদান করবেন না। আইনের হাত পা বাধা এখন আমাদের ছাত্রলীগকে ধ্বংশ করতে হবে স্বাধীনতা আনতে হবে আমার সোনার বাংলাদেশে। আমি হয়তবা আসতে পারি বড় ন্যায় প্রতিষ্ঠা করতে বড় আকারের দল নিয়ে।,1,politics
দেশটার হোগা মেরে যাচ্ছে এরা,1,politics
কুত্তার জন্ম আওয়ামীলীগ,1,politics
কাউয়া কাদের হা হা হা,1,politics
চোরের বাচ্চা এরা পুরাই লুটেরা বাহিনী এরা,1,politics
কাদেরের সাথে পাকিস্তানের চোদা খাওয়াটার কোন তুলোনা হয়না আর রুবিতো একটা সামা বিক্রী করা মেয়ে।,1,politics
হায় হায় চোদন লিগ,1,politics
কুতার বাচ্চারা বালের ছাএ লীগ,1,politics
কাইয়া কাদের খালেদা জিয়ার জুতার সমানোনা আর খালেদা জিয়ার সমান হয়কিকরে।,1,politics
লীগ গুলাই হলো আসল জঙ্গি,1,politics
নটি ঘূষ খোর উকিল আপূ নটি,1,politics
এই হিন্দু মহিলা বেয়াদব কোথাকার ফালতু জুতা দিয়া পিটানোর দরকার,1,politics
অপু কে ঝারু পিটা করা উচিত মিথ্যা কথা বলার জন্য সে একজন পতিতা ওবায়দুল এর বেড পার্টনার,1,politics
কুত্তা লীগ জারজ লীগ ছাড়া শিক্ষাব্যবস্থা চাই,1,politics
প্রতিবন্ধী ওবায়দুল কাদের,1,politics
এই ভাই তারেক যদি চুরি শিখায় তাহলে তোরা কি দাবি করির আওমীলিক তুই বাংলাদেশের নাগরিক খালেদা জিয়া বাংলাদেশের জন্য অনেক কিছু আছে ছাগলের বাচ্চা,1,politics
এই হিন্দু মাগিকে জুতা পেটা করে দাঁত গুলো ফেলে দেয়া দরকার কোথায় নোয়াখালীর রাম ছাগল অার কোথায় বেগম খালেদা জিয়া,1,politics
খালেদার সাথে কেনো তুলনা করেন। এতেই বুজা গেলো বাংলাদেশের মানুষ মূর্খ । কই রাজ রানী আর কই বিছনায় মুতনী। কাদের মাদারচুদ । কাদের বাইনচোদ। এই মহিলাকে মনে হয় কাদের চুদছে,1,politics
দর খানকির পোলাগ,1,politics
ছাত্রলীগের মাইরে বাপ। বেয়াদব পোলাপাইন,1,politics
কোথায় বেগম খালেদা জিয়া কোথায় কাওয়া কাদের । আমাদের একটা আঞ্চলিক কথা আছে কোথায় আদিনাথের পাহাড় কোথায় ছাগলে ঘাস খায়। ঠিক তেমনি বেগম খালেদা জিয়া আর কাওয়া কাদের তফাৎ।,1,politics
আওমীলিগ ফেরাউনের বংশধর,1,politics
আমার বালের খবর বলতে আসছে 😠😠,1,politics
শেখ হাসিনা মাগির বাচ্চা,1,politics
বেশ্যার ছেলের ও লজ্জা আছে বর্তমান ছাত্রলীগ এর লজ্জা নাই ! লজ্জা হয় এক সময় এই প্রাণের সংঘটন করতাম !,1,politics
এমপি মন্ত্রী পর্যায়ের লোক অনুষ্ঠানে নিয়ে এসে কথার মাঝে অনু্ষ্ঠান শেষ করে দেওয়া হয়। ধরে চুদা হবে যেদিন ঠিক হয়ে যাবা,1,politics
কুত্তার বাচ্চা শিকক্ষ,1,politics
খালেদা জিয়ার শাথে তূলনা কাউয়ার হায়রে দূনিয়া,1,politics
কাওয়া কাদের সাথে বেগম জিয়ার তুলনা শুনতে ও লজ্জা লাগে হায়রে বাংলাদেশ।,1,politics
এই মাদারচুদ হল একটা নাস্তিক। খাংকির পুত। তার জন্মের কোন ঠিক নেই।,1,politics
জংলি লীগ,1,politics
রাজনিতির সপ সুওরের বাচচা চোর,1,politics
কুত্তালীগের জারজরা একটু অপেক্ষা কর!! তোরা পালাবার সুযোগ পাবি না তোদের লাশ মিলবে নদীর ধারে বা কোন ঝংগলে,1,politics
হারামি,1,politics
পতিতালীগের নেএীরা এই রকম কথা বলবেই,1,politics
শালা কাউয়া মন্ত্রী তুই এসব কাজ করতে গেছিস কেন ? পাবলিক পিটানি খাবি তোর নিজের কাজ নিজে কর এসব তোর কাজ না শেখ হাসিনার পা চাটা গোলাম! সিফাতুল্লা ঠিকি বলেছে। তুই কাউয়া ঠ্যাডা কাদির শালা কুত্তা তুই।,1,politics
কাওয়া কাদের,1,politics
আমার সালা ওবাইদুল কাদের পোকির? মাগির চুদিয়া।,1,politics
কুওালীগ আগা লীগ হোগা লীগ,1,politics
শালা কাউয়া কাদের,1,politics
তুই চোর অপু খানকি মাগি,1,politics
বালের খবর,1,politics
শালা মূর্খ নিজেকে খুব জ্ঞানী ভাবিস মনে হয়??,1,politics
মনুষত্যহীন লোক হলো কাদের।শুধুই বিএনপি বিএনপি মাদারচোত,1,politics
কাউয়া কাদের রেডি হয়ে জাও,1,politics
বাল ছিড়ে দেবে নে বিএনপি,1,politics
কোথায় আগরতলা আর কোথায় পুন্দেরতলা বেগম জিয়া আর কাউয়া,1,politics
বেগব জিয়ার সাথে কার তুলনা।সরকার এর সাথে ! আসলে এরা কাউয়া।,1,politics
আপু ওকিল তোরে চদে হবে,1,politics
কাউয়া কাদের 🙄🙄🙄,1,politics
কুত্তালীগ শালা রা,1,politics
কাউয়া সবার চাইতে ডেঞ্জার খালেদা জিয়াকে মুক্তি দিলে কী তোদের আগুন জ্বলে???????????,1,politics
এই মাগি তোর বানানো কথা কি দেশের জনগন বিস্যাশ করবে সালী আওমীলিগের পা চাটা পাগলী,1,politics
এই মাগি খিন্দু কি বলে,1,politics
তুই কি বিচার করবে রে মাদারচোদ তুইতো একদম বাংলাদেশের সত্য তুই জমা শিবিরের ব্লগ,1,politics
রাস্তায় কি চায় ডিম মাগি গুলোর পাচায় দেওয়া উচিত,1,politics
পাগলা নুরা। নুরা পাগলা। ভএক্সোদ নুরা,1,politics
মাগী অপু উকিলের কাউয়ার লইগ্যা কা কা কা কা!,1,politics
ওবায়দুল কাদেরের সাথে খালেদাজিয়ার তুলনা করা যায় না খালেদা তো এতিমের টাকা মেরে খেয়েছে তাকে চোরের সাথে তুলনা করা দরকার।,1,politics
আসলে শালা একটা কাউয়া কাদের,1,politics
সবাই চোর,1,politics
জিয়ার নিকট কোটি আজ। কোটি তিনি কাজে লাগাবেন ।।। রাজাকার তো হাছিনার আপনজন। মাগী।তুই।মনে।রাখিস।।।,1,politics
হিন্দু সুনা কি বাল জানে,1,politics
ওই মাগী কাদের গলাটফেরেন,1,politics
ওবায়দুল কাদের তোর মায়রে চুদি অজুগ্গ মন্ত্রী চুন্নী হাসিনার দালাল।আর ইন্দুনীরে এই টকসুতে চুদিব।,1,politics
আরে হিন্দু শালিকে ভারতে পাঠানো হোক মোদিরের কাছে।,1,politics
আস্তা ছাগল অপ । কাৱ সাথে কাৱ তুলনা দেয় গাদা কোথাকাৱ,1,politics
নুরার পাছায় গরম ডিম চাই,1,politics
কিরে তর অপু কই খানকির পোলা,1,politics
কাউয়া কাদের নিজেইতো আসল লাইসেনস চিনেনা,1,politics
ডিম নুরুর দুই গালে জুতা মারো তালেতালে,1,politics
আরে ভাই এরা তো ছাত্রলীগ না তারা হলো কুত্তালিগ তাই কুত্তার মত আচরণ যত দিন হাছিনা কে ক্ষমতা থেকে সরানো যাবেনা তত দিন বাংলাদেশের মানুষ নির্যাতিত হবে এই সব সস্ত্রাসীর হাতে ।,1,politics
কুত্তালীগকে কি বলব ভাষাই হারিয়ে ফেলছি এগিয়ে যান নুর ভাই,1,politics
এই শালারে আওয়ামীলীগের পদ থেকে বের করে দিলে দুইদিন পর শিবিরে যোগ দিবে।,1,politics
অপু উকিল নাকি বালের উকিল তোমাদের কি লাজ সরম একেবারে নাই।তোমরা কি চোখে দেখো না জনোগনকে তো মানুষ শিখাইয়া দেয় না।পেইজ বুক ইউটুবে তোমাদের জনোগন জুতার মালা দেয় কি পরিমানে গিন্না করে একটু দেখো না।সরম থাকলে টকশোতে বসে বড় বড় মিথ্যাচার করতে না।রাতের বেলা ভোট ডাকাতি করে জনে মিলে ভোট দেয় শত লজ্জা করে না।অার তোদের লজ্জা করবে কি করে তোদের লজ্জা অাছে নি।কোথায তিন তিনবারের প্রধান মন্তী অার কোথায় কাউয়া কাদের সেইটা নিয়ে তুলনা করো।তোমরা মানুষ নাই তোমরা অমানুষে পরিনতো হয়ে গেছো।মানুষ হওয়ার চেষ্টা করো অাজ মরলে কাল দুইদিন।কেন এতো হিংসা করে বছর বয়েসি মহিলাটাকে মিথ্যা মামলা দিয়ে অাটকিয়ে রেখেছে ডাইনি হাসিনা একদিন এর ফল ভোগ করতে হবে হবেই পাপ বাপকে ও ছাড়বে না।,1,politics
আসলে তোরা একটা জারস সন্তান আয়ামিলিক কার সাথে কার তুলনা করিস তোরা তোদের বিবেগ বুদ্ধি হারিয়ে গেছে,1,politics
জয় কুত্তালীগ জয় হোক আর জয় হুক কুত্তালীগ,1,politics
মালাউন মিথ্যাচারি মাগী মিডিয়ার সামনে মিথ্যা বলতে হিসাব করে বলতে হয়,1,politics
কোথায় ওবায়দুল কাদের আর কোথায় খালেদা জিয়া আসলে ক্ষমতার এতটাই অন্ধ হয়ে গেছে একটা গরুর সাথে একটা মনের মানুষের তুলনা করে ওবায়দুল কাদের একটা গরু না হলে কথা বলে ?,1,politics
ছাত্রলীগ মানি একটা মাদারচোদ লিগ কুত্তার বাচ্চাদের মন চায় জোতা দিয়ে মারতে মন চায়,1,politics
আমি কাতার থাকি আমি দশ হাজার টাকার গড়ি কেনার ক্ষমতা নাই তাই বলে কি তুকে গালিবো নাকিরে খারকির পোলা শুয়রে বাচ্চা তার থলিতে তুর বৌয়ের ব্রা আছে।,1,politics
কুত্তালীগ গুলোর বিচার হবেই ইনশাআল্লাহ।,1,politics
বেশ্যার ঘরে জন্ম নেওয়া সব গুলো ছাত্রলীগ করে,1,politics
রুমি সোসাইটির অন্যতম প্রধান ছাগল,1,politics
খানকি মাগি ব্যাংক লুট করস তো তোরা সেক্সিনার গ্রুপ শুয়্যার😠🔨,1,politics
সময় টিভি তোর সোনার ভিডিও আমি দেখলাম না কারন একটা চোরের বাচ্চা জারস এর সাথে এক জন ভালো মানুষ এর তুলনা করিস সালা তোর ভিডিও ডিটিট কর কইলাম মালয়েশিয়া থেকে বম মারুম তোর কপালে,1,politics
তুমি যে বোকাচোদা কথা কস ফটো ফটো তুমি কি তুমি কয়টা মারতে ছো,1,politics
সব গুলা চোদোন খাইতে গেছে,1,politics
কাদিরার আয়ের উতস হল ইয়াবাখোরদের থেকে চাদাবাজি। মাগি ব্যবসায়ের থেকে চাদাবাজি। দলের কোন পদ দেয়ার জন্য টাকা নেয়া। বিভিন্ন টেন্ডারবাজিতে টাকা নেয়া ক্যাসিনো জুয়াড়িদের থেকে আয়,1,politics
কি বালের মধ্যে ভিপি হলো খালি মাইর খায়,1,politics
কুত্তা কাদের।,1,politics
ওই হালা হাছাই কাওয়া,1,politics
এই ইদু বিটির কপালের সিঁদুরি আমি পেসাব করি,1,politics
এরে শালার ভাই তুই আমেরিকাতে একজন বালের ব্যবসায়ী। তুই কি ব্যবসা করিস? আসলে তুই একটা দালাল। ইউটিউবার দালাল। ইউটিউবার ফকির। ইউটিউবে কিছু ভিডিও দিয়ে সেখানে কামাই করে চলিস। তা না হলে কাদেরের ঘড়ি নিয়ে এতো আলোচনা কিসের। বাংলাদেশে এখনো হাজারো লোক আছে যারা এর থেকেও দামী দামী ঘড়ি কিনে ব্যবহার করে থাকেন। তুই যে ঘড়ির দাম বলেছিস এগুলো কি কোন মানুষ তাকে উপহার হিসাবে দিতে পারে না? সব ঘড়ি কি কিনতে হবে? তুই কার দালাল সব কিছু তোর শেষের দিকের কথায় বুঝা গেছে। আসলে তোদের মত অকর্মঠ বলদ মার্কা লোকদের এই কাজগুলো করাই স্বাভাবিক। তুই সব জানিস বাল জানিস বাইনচোদ।,1,politics
শালী মাগী তাহলে কেন জিয়া কে কেন বঙ্গবন্ধুর সাথে তুলনা করিস?,1,politics
বর্তমান ছাত্রলীগ রা কুক্তার মত ব্যবহার হয়ে গেয়ে।,1,politics
ওবায়দুল চোর,1,politics
তুই যে একটা পচা শামুক তুই এর সম্পর্কে জানলি কিভায় সা লা আবাল,1,politics
মা মা মা জতোই করোচ নোয়াখাইলার পেচে পরছো ওরা নার কাডার জাত জাপানি,1,politics
কাউয়া কাদেরের সথে বেগম খালেদাজিয়ার তুলনা বেপারটা হাস্যকর।।।😀😀😀,1,politics
এই পাগোল চোদা নাটোক চোদাই তে নামছে রাসতায়,1,politics
হাসিনারে চুদি,1,politics
শালা কত দিন নাটক করবি আল্লার গজব পরবে একদিন,1,politics
ছাত্রলীগ যুবলীগ কুত্তালীগ হাতে কেউ নিরাপদ নয়,1,politics
বেগম জিয়ার সাথে ওবায়দুল কাদেরের তুলনা ব্যাপারটা হাস্যকর। আর কাউয়া কাদেরের তীব্র জনপ্রিয়তার চোদনে আমরা দাঁড়াতে পারছি না ।,1,politics
ওকিল কুততার বাচছা।সুয়েরের বাচছা,1,politics
বালের পরিবর্তন করতে আওয়ামী লীগ কুত্তালীগ করে চুরি করে ক্ষমতায় গেছে কুত্তালীগ,1,politics
লোক দেখানো ভন্ডামি করতে যেও না কাউয়া মন্ত্রী!,1,politics
কা কা কা কা কা কাউয়া টায়ার কাদের,1,politics
ভাদাইম্যা কাউয়া কাদের,1,politics
হিন্দু খানকিরে ভারত পাঠা,1,politics
এই বেসসা লীগ এর জন্য দেশ আজকা।। অসাতলে নেমে যাচ্ছে,1,politics
কাউয়া কাদের তোরে সামনে পাইলে জুতা পিটা করাই দেশ থেকে বের করে দিতাম,1,politics
হা হা হা কুততা লিগ,1,politics
মাদারী নিজেই রাস্তা ব্লক করে রাখছে 😣,1,politics
কাউয়া কাদেরত একটা কুকুরের সমাতুল্লোও নাই আর ঐ শালারা হাসেনার মুত খাওয়া এই টকশো,1,politics
এ চুদানির পুত একটা কুলুংগার শেখ হাসিনা এ গুলা কি দেখেন না,1,politics
অপু উকিল মহিলাটার লজ্জা শরম বলতে কিছু নাই ? কেমনে কথা বলে এই চুত্মারানি?,1,politics
ছাত্র লিগ না বলে কুত্তা লীগ বলেন,1,politics
গুন্ডালিগ,1,politics
কাউয়া কাদের তো বেহুঁশ হয়ে না যাই । পদ হারালে কাউয়া কাদের কা কা করা বন্ধ হয়ে যাবে ।।। হা হা ।,1,politics
তুই কি জানিস তুই একটা বোকাচোদা🤬🤬,1,politics
জুতা মার মাগি পুত কুকুর বাচ্চা কুকুর আওয়ামী লীগের কুকুর ওসি দালান,1,politics
ডেডা মাগি বেয়মান,1,politics
বঙ্গবন্ধুর আদর্শের স্লোগান দিয়ে জনগণের টাকা লুটপাট করে নিয়ে উন্নয়নের রোল মডেলের দেশ এখন ।বঙ্গবন্ধু বেচে থাকলে শেখ হাসিনাকে গুলিকরে মেরে কুত্তাকে দিয়ে খাওয়াতেন।,1,politics
এই কুত্তার বাচ্চা ছাত্রদের সাথে এক দিনও আসে নাই কেন? কে জবাব দিবে?,1,politics
এই মাদারচোদ অপু কোথায়,1,politics
মাদার চোদ গো অবস্থা দেকলে নিজেকে সামলাতে পরিনা,1,politics
ওবায়দুল কাদের তো জারজ। তার বাপ অনেক,1,politics
কুত্তালীগ কি সাধারণ জনগণের চেয়ে কি বেশি ডিম মারা জানে নাকি।,1,politics
আমার হেডার পুতের কান্দে ছাতি ।কাউয়া।,1,politics
নূর খানকির পোলা জামাতের দালাল,1,politics
আগামীতে উনাকে ট্রাফিক পুলিশের কাজ করবে বলেই উনি মাঠে নেমেছেন সালা চোরের বাচ্চা,1,politics
সালা তুই হাত লাড়াবি না,1,politics
তোই নিজেই তো একটা নাস্তিক কুত্তার বাচ্চা নিউজ করার আর জায়গা পাস না জিনিস খুঁজে পাস না বিনা ভোটে সরকার মানে কি????,1,politics
খালেদা জিয়ার সঙ্গে ওবায়দুল কাদের তুলনা এই কোন পাগলের বাচ্চা ওরে জুতা দিয়ে বাইরে নেয়া উচিত ফটো অশিক্ষিত বর্বর ওরে পাবনা পাঠাইতে বে,1,politics
মাদার অফ ক্যাসিনোর জারজ যুবলীগ ছাত্রলীগ থাকতে বছর পর কারা আওয়ামীলীগকে নেতৃত্ব দেবে সেটা নিয়ে এত ভাবনা কিসের?,1,politics
খালেদা বু বু একজন অশিক্ষিত মাগি,1,politics
কোথায় প্রধানমন্ত্রী আর কোথায় কাউয়া কাদের পাট ব্যাপারী।,1,politics
অপুকে নতুন করে খানকি পারা ও পারার সরদার বানানো হক,1,politics
শালা কুত্তালীগ দলটাকে কেন খালা আম্মা হাসিনা কেন নিষিদ্ধ করেননা,1,politics
তোই কি তোর সামিকে রাতে সময় দেচ নাকি তোর মাথায় কপর কৈ মাগি,1,politics
অপূ খানকি,1,politics
কানকি পোলারা পড়া লেখা শিকতে আইছ,1,politics
শালা তুই আসলে কুত্তির নাজায়েজ বাচ্চা ফইন্নির খবর নিয়া আইছে,1,politics
মুচির পোলাপান কুত্তালীগ করে,1,politics
ঢাকা বিশ্ববিদ্যালয়ের মেয়েদের আচরন নডি পাড়ার মাগিদের মত কেনো,1,politics
সবাই মাগি,1,politics
খালেদা হল পাকিস্তানের জংগি জামাত রাজাকারের যৌনদাসী শালী নোয়াখালী তে হিন্দু মেরেছে শুয়োরের বাচ্চা,1,politics
এঔ হিজলা অপু তোর মায়রে ঘোরা দিয়া চুদাদিলে তুই ঠিকহবি,1,politics
ভিপি নুর একটা রাজাকারের বাচ্চা । এর প্রমান হচ্ছে ভিপি নুরের উপস্থিতিতে। শেই জংগী সন্ত্রাসী রাজাকার জামাত বিএনপির স্লোগান দিতেছে আগুন জালাও। পাকির দালাল শিবির কেডার ভিপি নুর মুর্দাবাদ । দেশ বিরোধী যুদ্ধাপরাধীরা সব নিপাত জাক। বাংলার সকল শিক্ষা প্রতিষ্ঠান মুক্তি পাক।,1,politics
কাওয়া কাদের তকে জুতা পেটা করবো হালা।।।,1,politics
কোথায় লুচ্চা কাদের কোথায় খালেদা হায়রে দেশ,1,politics
আওয়ামী লীগ মানেই চোর বড় বড় কথা চুদায় মাদারচোদ গুলা রাজাকারের বাচ্চা রাজাকার আসল রাজাকার এখানে কোন আওয়ামীলীগ মাদারচোদ ঘেউ ঘেউ কোরিস না খানকিরপুত👍👍👍 আন্ডার না করিস,1,politics
এই নুরু শুয়ারের বাচ্চা পাগল নাকি একেক বার একেক কথা বলে,1,politics
অপু উকিল পতীতা মেয়ে শালী পুত শালি অপু উকিল ।।।। কাদেরের ধন নে শালি,1,politics
কই খালেদা জিয়া আর কই কাউয়া কাদের,1,politics
কাউয়া কাদের কাউয়া কা কা কা,1,politics
শিক্ষিত সমাজ যদি এরকম হয় তাহলে আমাদের মতো রাখালরা কি করবে? বাইনচো* লীগের কারনে আজ পুরো ছাত্রসমাজ অধপতনের দিকে।শিক্ষকরা সন্ত্রাসদের কথায় উঠছে বসছে এদের কাছ কেমন শিক্ষা অর্জন করতে পারবে ছেলেরা!আর ওখানে যে ছেলেটা মেয়েদের সাথে অকথ্য ভাষায় কথা বলছিল হালার পা* দিয়ে গরম ডিম হান্দানি উচিৎ ছিল!! একসময় ভাবতাম ঢাকা ভার্সিটি একটা শিক্ষার্থীর জিবন বদলে দিতে সক্ষম কিন্তু বাস্তব ভিন্ন!,1,politics
মিথ্যেবাদী বেঈমান মাতারি কিভাবে বলে ক্ষমতা দখল করেছে বিনপি। কুত্তার বাচ্ছা ।,1,politics
হিজরাদের মত হাঁটে ।,1,politics
চোরের গলা একটু বড় হয় ঠিক তেমনই অপু উকিলের গলা বড় হয়ে গেছে! বেয়াদব মহিলা!,1,politics
এই সব জানুয়ার লীগকে গুলি কটে মারা দরকার।,1,politics
কাউয়া কাদিরে মনে হয় নিচ দিয়ে পানি আইছে।,1,politics
ওবায়দুল কারের রে বিতারিত করা হুক সালায় একটা ঝর আসলেও বলে বিএনপি জামায়াতের চাল একটস বিল্ডিং ধস হলেও বলে বিএনপি জামায়াতের চাল সালা আবাল সুদা,1,politics
ছাএলীগ সালা দের নিসিদ্দ করা হক,1,politics
আমি চুূদতে চাই উকিল কে খানকির,1,politics
এই মাগী তুইতো তারেকের রাতের খাবার।,1,politics
ছাুএলীগ আর কুকুর এর মধ্য কোন পার্থক্য নেই,1,politics
লেওরা মারকা টিচার,1,politics
বিদেশে বসে কুকুরের মত ঘেউ ঘেউ করা তোদের কাজ। অপপ্রচারে কাজ হবেনা।,1,politics
"হে,গর্তবাসী বৃদ্ধ জাফর ইকবাল ষার।হে,লুচু বৃদ্ধ। আর কতকাল ফাপর মারবেন?",1,celebrity
ছাগলের বাচ্চারা না বুঝেই মদখোরি কমেন্ট করে যাচ্ছে,1,celebrity
মাদারচোদ একটা জাফর ইকবাল,1,celebrity
"ছাগুরা এখানে এসে বমি বমি করছে। ওদের জন্যে শুভ কামনা। দেশে কাঁঠাল পাতার বড়ই অভাব, তাই ছাগুরা এখানে এসে চেঁচামেচি করছে। 😂😂😂",1,celebrity
চুদার সুশীল আসছে,1,celebrity
তুদের মত কুওাদের উচিত শাস্তি দেওয়া হবে,1,celebrity
ভূতের বাচ্চা জাফর 😜😜,1,celebrity
খাআআআনকির পোলা..,1,celebrity
তোর মাইয়ার হে  ডা,1,celebrity
কিরে শুয়োর ছানা কই তুই?😡😡,1,celebrity
#সরকারের_দালাল,1,celebrity
জাতি আপনারে কমেন্টে ঠস ঠস চুদসে আপনি কি সেটার আওয়াজ শুনেন 😜😂😂 নাকি মদ খেয়ে সৃতি ফিরাচ্ছেন 😂😂,1,celebrity
"১৯৭১ সালে টাঙ্গাইল এর ১২ বছরের শিশু শহীদুল ইসলাম লালু যখন জীবন বাজি রেখে পাকিস্তানি ক্যাম্পে ঢুকে বাংকারে গ্রেনেড চার্জ করছিল, আপনি ১৯বছরের টগবগে যুবক জাফর ইকবাল তখন পাকিস্তানিদের হাত থেকে বিপদ কমাতে নীলক্ষেতে গিয়ে লম্বা চুল ছোট করছিলেন। আর এখন সৈরাচারের দালালি করে মুক্তিযুদ্ধের চেতনা চু..দান। বাইঞ্চুদ।",1,celebrity
"তুইতো নিখাদ গণ্ডমূর্খ,  এক ফোটা জ্ঞানের আলো তোর মধ্যে নেই। যদি থাকতো তাহলে  ভোট ডাকাতিকে  তুই সমর্থন করতিনা।  তুই পা চাটা গোলাম।  নৈতিক মূল্যবোধহীন পশু।",1,celebrity
তুই তো হালা গান্জা খাইয়াই কুল পাস না টুকিটুকি ভাবনা চুদাবি কখন।😂😂😂,1,celebrity
- চ্যার দয়া করে বমি করার সময় পলিথিনে করবেন আর সেটা বাসায় পার্সেল করে নিয়ে যাবেন! - আপনার বমির গন্ধে জনগন কিন্তু অজ্ঞান ওয়ে যাবে!! - কুবই বমিপ্রবন মানুষ আপুনি! :/,1,celebrity
ষার আশ্চর্য জাফরা দ্রোনাচারিয়ার নির্রবাাচনের এই দশ ইশতেহার কে দিয়েছে   কে  কে কে?????,1,celebrity
চুচীল চুদায়,1,celebrity
"জাফর সাহেব আপনি এযুগের নব্য রাজাকার। গুম হওয়া তরুণ ছেলেদের মায়েদের চোখের পানি, সন্তানের অভিশাপ আর স্ত্রীদের হাহাকার একদিন এদেশে আপনার মত মিষ্টভাষী জঙ্গির বিচার করবে। হুমায়ুন আহমেদ বেঁচে থাকলে বলতো জাফর তুই রাজাকারি বন্ধ কর. তুই রাজাকার জাফর তুই রাজাকার।",1,celebrity
মাগীরপোঁয়া তুই ২৪ বছর শিক্ষাব্যবস্থার সোগা মেরে গিয়েছ ??,1,celebrity
একবারে ভাল মানুষ সেজে বসে আসে। তোদের মত কিছু ছাগল এর কারনে প্রশ্ন পত্র আগের দিন পাস হয়। কথা আসে না চোরে চুরি করলে সবার সামনে থেকে করতে পারে। শিক্ষা মন্ত্রনালয় যত সেষ্টা করুক প্রশ্ন পত্র জেন পরিক্ষার আগে পাস না হয়। আর তোমাদের মত কিছু ছাগল আসে জারা প্রশ্ন পত্র কি ভাবে পাস করা জায় সে ধান্দায় থাক। আর সাও জে সরকার কে কি ভাবে অপবাদ দেওয়া জায়।,1,celebrity
দুরূ হালার ঘরের হালা বাইনচোদ,1,celebrity
আপনার মতো নোংরা কিছু ব্যক্তির জন্যেই আমাদের আজকে  এই অবস্হ্যা।,1,celebrity
"বেশ্যাবেডা,  তেলমারা বন্ধ কর। তোদের মতো তেলবাজদের জন্য  দেশের আজ এই হাল।",1,celebrity
"চৌইয়ার পোস্ট কার বালে পড়ে, আইছি কমেন্ট এর টানে।",1,celebrity
লুইচ্চা মাদার ফাকার তোর আসল রুপ পোলাপান বুঝতে শিখছে।,1,celebrity
তোরে কে চোদে রে....?,1,celebrity
দেখা যাক ছাগুর দল কমেন্টে আজ কেমন বিনোদন দেয়,1,celebrity
এই একটা গল্প লিখতে পাচ দিন সময় নিছোস! বাইঞ্চোদ জীবনে উন্নতি করবি ক্যাম্নে?,1,celebrity
একটুখানি চাওয়া -- দালালের মুখে দেই আমাদের পাছার হাওয়া!,1,celebrity
ছাগুরা কিলবিল কিলবিল করছে!!!,1,celebrity
আরে কানার ঘরের লেংরা চিটিংবাজ মাসের পর মাস যখন তুমি আর এমরান এইচ সরকার ও লীগের চেলাচামুন্ডারা সাহাবাগ চত্তর ব্লোক করে রাখছিললা তখন তোমার এ বিভেকবোধ কোথায় চিলো।,1,celebrity
তরে দেশের মানুষ গোয়াও মারব না বাইঞ্চুত,1,celebrity
হালা এম সি এর বাচ্চা বি সি,1,celebrity
"স্যার,,,আপনি নির্লজ্জ, আপনি কুকুর!",1,celebrity
"চোদনাবাগীর চেতনা এতোক্ষনে জেগে উঠেছে।ভালো একটা গল্প ফেদেছে এতোদিনে।এটা কোন প্রকাশনীতে দিলে ভালো টাকা পাবেন।কি দরকার আপনাদের?ছাত্ররা যেখানে সেখানে আপনার মতো মানুষের দরকার আছে কি?একটা প্রশ্ন আপনার কাছে, আপনি কি শিক্ষক হওয়ার যোগ্য?",1,celebrity
হ্যালো মেরুদণ্ডহীন বাইনচোদ বুড়ো খোকা 😎✌,1,celebrity
"মনে করেছিলাম আপনি ভালো মানুষ,কিন্তু আপনি একজন চাটুকার,দালাল।আর দালাল কখনো ভালো মানুষ হতে পারে না।",1,celebrity
সরকারের পা চাটা দালাল ছাড়া কিছুই নন আপনি? দিতে থাকেন তেল - উপরে উঠতে হবে আপনাকে। মনুষ্যেতর লেবেল যতই নিচে নামুক না কেন?,1,celebrity
টিনের চালে কাউয়া তুমি একটা শাউয়া,1,celebrity
"জানো গালি খাবা,তাও লিখলা ক্যান সুদির ভাই!",1,celebrity
ছাগুমুক্ত স্বদেশ চাই,1,celebrity
। স্যার একসময় আপনার অনেকক ভালো একজন ফ্যান ছিলাম। বাট আপনার দালালি গুলা চোখে লাগার পর আর ভালো লাগেনা।,1,celebrity
বাইঞ্চুত নাকি একটা গালি।  পুলাপাইন কুব কারাপ..,1,celebrity
"ছার, ও ছার। আসেন দুদু পেগ মেরে আবার গর্তে লুকাই আমরা। যদি পারেন কালকে ঢাকা এসে নিজের লুইচ্চ্যা খোমাটা সবাইরে দেখায় যাইয়েন।",1,celebrity
তোর হেডা মাগীর পোলা,1,celebrity
তুমি একটা বালের লেখক।,1,celebrity
এই মাদারচোদ নাকি আম্লিগ না.....,1,celebrity
এই চুদাটা ভাট্টিকে চুদার দরকার ছিল।,1,celebrity
"তুই শ্লা উন্মাদ।হুমায়ূন আহমেদের ভাষায় বললে,বদ্ধ উন্মাদ।যে দেশে ধর্ষণের বিচার ভালমতে পায়না মা-বোনরা।সেখানে তাদের চাকরির ক্ষেত্রে বেতন কম নিয়ে নাক গলাচ্ছিস?এটা কিভাবে সম্ভব? যেখানে তাদের দেহের নিরাপত্তাই নাই।আত্নার নিরাপত্তা নাই। ওরা বেতন চায়না দেহের নিরপত্তা চায়।  যেদেশে কলজ ভার্সিটিতে ছাত্রী - শিক্ষকের মধ্যে অশ্লীলতা চলছে।সেদেশ কখনো সুশিক্ষিত জাতি উপহার দিতে পারে না।মূলত নারীশিক্ষা বিরোধী না।তোদের মত কিছু লুচ্চা টাইপ শিক্ষকদের শালীন হওয়ার জন্য একথা।",1,celebrity
"ছএলীগ তো তোর বউরে কামড়াইছিলো,তুই হালা এতদিন ধরে খালি হড় হড় করে বমিই কইরা গেলি ?  কোদাল দিয়ে শাবিপ্রবি'র আশেপাশে গর্ত করে লুকিয়ে থাক,কখন জানি কোমলমতি দেশ সুদ্ধ করার যুদ্ধে নামা আদরের ভাইবোনগুলাই তোর ধনের(ধ্রোনের) লাইসেন্স চাইয়া বসে তার হিসাব নাই !",1,celebrity
"-ষাড়😎 দুই এক লাইন পড়ার পড়, কমেন্ট গুলো দেখে বড় অফাক হইলাম 😲😲",1,celebrity
"হালা রাজাকার,,। তার বর বাই ত,মেয়ে বান্দবী কে বিয়ে,,  তার কাজ থাকে আর বালো কথা কি আশা করা জায়,,",1,celebrity
চুদনা ফলো দিয়া গেলাম পড়ে পড়ুম😇😇😇,1,celebrity
ছ্যাড় আপনার পয়দা ঠিক আছে?দাড়ি নাই গোফ আছে? মাদারসোদ,1,celebrity
খানকীর পোলা তুইতো লীগের  পা চাটা গোলাম!  তারপর ও তোর উপর হামলা ছাত্রলীগই করপছিলো মনে নাই???  দেশের স্বার্থে মুক্তিযুদ্ধ  হলে ৭৫ সালে সংবিধানের  ৪র্থ সংশোধনী হয়েছিল কেন???  এনালগ বাকশালী কায়েম করেছিল কেন মজিবুর রহমান????,1,celebrity
ওহে চেতনার আগারবাতি গত২/৩দিন কোথায় ছিলেন আপনার লিখার অপেক্ষায় জাতী এখনো মুখে কুলুপ আটেনি.....চাটুকারিতা পারেন বটে,1,celebrity
আবালচোদা কি কমেন্টগুলো পড়তেছে না! !,1,celebrity
"আমার বাসায় টেলিভিশন নাই,,,,😞 ওরে শ্লারপুত তোর ইনকামের টাকা গুলা কি তোর পুটকিতে ডুকাচ😌🐸  বিঃদ্র:- বাংলাদেশে রিক্সাওয়ালার ঘরেও এখন টিভি থাকে!",1,celebrity
স্যার আপনি চুতিয়া,1,celebrity
ছাএ রা কি বলেছে আমি রাজাকার আয়মী লীগ রাজাকার বলেছে  নটির ভাচচা,1,celebrity
মিষ্টার ষাঁড় আপানি যে তীতৃয় লিঙ্গের বেশ্যা তা আগে যানতাম না😝😝😝  হ্লার্পুত শিক্ষিত কীট 🤪,1,celebrity
তর মত লেখক কে অামি চুদি,1,celebrity
৮.মিনিট ১৭সেকেন্ড পর্নো ভিড্যাু দেখে তুমার উপর বীর্য পাত করা উচিত,1,celebrity
আপনি তো ধর্ষন লীগের দালাল!!!,1,celebrity
"তুই কৌশলে ভোট ডাকাতিকে জাস্টিফাই করছস গণধর্ষণের ঘটনার নিন্দা করার উসিলায়। তোকে শুয়োর বলবোনা, তুই বুইড়া বরাহ নন্দন।",1,celebrity
জারজের বাচ্ছারা অনেকদিন পর খাবার পেয়েছে।তাই কমেন্টবক্সে হুমড়ি খেয়ে পড়ছে।তাই কেউ বিভ্রান্ত হবেন না।,1,celebrity
"খানকির পোলা কোন গর্ত থেকে উঠে আসছস। তোর মত নাস্তিকেরর বাচ্চা, দালাল সরকারের সোনা লেহনের টাইম পাস। পোলাপান যুক্তিত আন্দোলন করলে সেখানে বমি চোদাস।",1,celebrity
খানকি,1,celebrity
"তোরা শুওরের উরশে জন্ম নেওয়া প্রজন্মরা ট্রল করতেসস কর, হেডামে তো একটা বালও ছিড়তে পারস না সরকারের। যা করবি স্রেফ কমেন্টে পারবি আরকি।",1,celebrity
তুই একটা মাদারচুদ,1,celebrity
"কুত্তার বাচ্চা,তুই কই এখন।বমি করতেছস",1,celebrity
"জাফর ইকবাল তুই চোর,  মুক্তিযুদ্ধের সময় তুই চুরি করে গর্তে লুকিয়ে ছিলে",1,celebrity
"১৯বছরের দামড়া ট্রেঞ্চ খুড়ে বসেছিল,",1,celebrity
":: খালেদা জিয়ার ৩৯ তম জন্মদিন !  ১৯৭৫ সালের ১৫ অগাস্ট যদি জাতির জনককে হত্যা করা না হতো; তাহলে আজকের এই কথিত খালেদা জিয়ার জন্ম হতো না। অনাম্নী থেকে যেত অখ্যাত এক হাউজ ওয়াইফ হিসেবে।  সেইদিক থেকে ১৯৭৫ সালের ১৫ অগাস্ট অষ্টম শ্রেণী পর্যন্ত পড়া এই কিচেন মেডের হঠাত জন্মদিন। কৃতঘ্ন খন্দকার মুশতাক রাশির দলদাসেরা এই- ""কিচেন মেড কেন রাজরাণী"", জন্মদিন যাত্রায় দলে দলে যোগ দিন।  https://www.facebook.com/photo.php?fbid=10203908210322032&set=a.1549967065497.2082905.1124712218&type=1&relevant_count=1",1,celebrity
"বিকৃত মস্তিষ্ক, বিক্রিত মাল, বমি বাবা জাফর ইকবাল।",1,celebrity
জাফর তুমি প্রতারক। তুমি দেশদ্রোহী। তুমি মানুষরূপী একটি ইবলিশ শয়তান।,1,celebrity
ছাগুদের কমেন্ট পড়তে আসছি,1,celebrity
ছাগু প্ললীর বাসিন্দারা বাঁশের কেল্লার খোঁয়াড় ছেড়ে এখানে ভিড় জমিয়েছে 😂  এদেরকে কেউ কাঁঠাল পাতা খাইতে দে।,1,celebrity
"খানকির পুলা বমিওয়ালা গর্ববতী, গোঁফ ছিড়ে পুটকিতে ভইরা দিমু, যেন পাদতেও না পারিস🐄",1,celebrity
তুই একটা মাদারি টোস্ট,1,celebrity
কনডম ফুটে অাবার জন্ম হইছে তার... ইস! অল্পের জন্য তার জানাযাটা পড়া হলোনা।,1,celebrity
"কুকু‌রে পে‌টে ঘি হজম হয় না ব‌মি অবধা‌রিত ,দু:খিত স্যার আপনার জন্য, আপ‌নি এগি‌য়ে যান,ছাত্র ছাত্রী‌দের কি প‌রিমান কষ্ঠ, অর্থ, সময় লাগব হ‌বে য‌দি আপনার ধারনার  ম‌তে এক সা‌থে পরীক্ষা টা হয়,",1,celebrity
জনাব দালাল,1,celebrity
আমি রাজাকার আর আপনি জানোয়ার।,1,celebrity
চুদ মারানি তুই কি বালের ফিজিক্স বই লেকসু যে কনো বালই বুজিনা।।।।,1,celebrity
হালা কসাই,1,celebrity
ছাগল ইজ ব্যাক,1,celebrity
স্যার মাত্র মদ খেয়ে আসলাম কিন্তু মাগী পাচ্ছি না 😞 তাই দয়া করে আপনে একটু আসবেন আপনাকে একটু চুদবো.. ✌,1,celebrity
খানকির পুত জাপর । কম নে ফাপর ।😆,1,celebrity
হেডার ঘরের হেডায় বমি কিতা তাও মনে হয় চিনে না😡,1,celebrity
"_ দেশের কয়েকজন কুলাঙগারের মধ্যে জাফর ইকবাল একজন , আ'লীগের দালাল|",1,celebrity
শালারপু‌তের লেখার ম‌ধ্যে কোন সৃজনশীলতা নাই। সব চুর‌ি ক‌রে বি‌দে‌শি বই থে‌কে।,1,celebrity
হালার ফালায় মরে নাই,1,celebrity
জাফর ইকবাল হচ্ছে আওয়ামী কুকুরের বাচ্চা। এবং তিনি মুরতাদ।,1,celebrity
খানকির পোলা তুই এখনো মরিস নাই😡😡😡,1,celebrity
স্যার আপনি এত বোকাচোদা কেন ??,1,celebrity
কিছুদিন আগে স্যার বলছিল....আমি সহজ সরল রাজনীতির কিছু বুজি না।আজ স্যার পুরা বাংলার রাজনীতির ইতিহাস লিখে ফেল্ল..... আমি বোকাচুদা নাকি স্যার বোকাচুদা এটাওতো বুঝতে পারলাম না।😆😆,1,celebrity
বাংলাদেশকে ধংসের জন্য ষাঁড় জাফর ইকবালের মত কিছু মিথ্যাবাদী কুলাঙ্গারই যথেষ্ট।,1,celebrity
শুয়োর বাচ্চা তুই একটা। আমরা এড বড় বিপদ থেকে বেঁচে গেলাম। দেখলাম না তোর একটা পোষ্ট।,1,celebrity
ভোদার গ্লানি বিশাক্ত!,1,celebrity
(((((((((((শুয়ার))))))))))))),1,celebrity
ষার একজন vvip মানে বুঝস? very very important person মদ খা মোরক্ষ চোদারা মদ খাবি মানুষ হবি শুঁটকি খাবি হড় হড় করে বমি করবি মোরক্ষ ছোদারা,1,celebrity
"তোর মুখে কাকে হাগুক,,বিড়ালে মুতুক,কুত্তায় পাদুক😜",1,celebrity
এদেশে কত পার্সেন্ট লোক শুয়োরের বীর্যের ফল তা বিভিন্ন লিখক ও সেলেব্রেটির কমেন্ট বক্স ও দেশের আকাম কুকামের অবস্থা দেখে বুঝা যায়।  ৯০% মুসলমান দেশের এই অবস্থা দেখে সবাই বলেন সুবানাল্লা।,1,celebrity
"তুই একটা বলদা কিসিমের লেখক,তোর মত বিবেকহীনকে মানুষ কেন স্যার ডাকে আমার বোধগম্য নয়।",1,celebrity
"জারজ শিবির আর বিএনপি ছাগলের দল এরা রাজপথে স্থান না পেয়ে, দেশে মানুষ ও বিদেশী বন্ধুদের কাছে স্থান না পেয়ে, ফেইসবুকে কে নামে বেনামে ফেইক আইডি খুলে গুজব মিথ্যাচার আর গালিবাজি করে.. এরা পাকি বীর্যের কিট পতিতাতলে জন্ম এদের জারজ গুলো কোন দিন আর বাংলাদেশে মাথা উচু করে বাঁচাতে পারবি না,, খুনি ধর্ষন, গোলাম আযম, নিজামী, সাইদী রাজাকারদের চোদনে এতিমের টাকা চোর খালেদার ওরজে জন্ম পতিতালয়ের সন্তান গুলো এখানে হাহাহা রিয়েক্ট্য ও বাজে কমেন্ট করছে..",1,celebrity
"সরকারি উচ্ছিষ্টভোগী, ভুয়া চেতনাধারী, ওপারের দাদা বাবুদের দালাল।  আন্দোলন ফলপ্রসূ হবার পর এখন গর্ত থেকে বের হয়েছে।",1,celebrity
"—ঠক ঠক ঠক —কে?  —খাঁটের তলা থেকে বের হন৷ ভয় নাই, যুদ্ধ শেষ। শীতকাল এসে গেছে  —আহা!  জাফড় ষাড়ের অসমাপ্ত আত্মজীবনী😪",1,celebrity
"ওপারেও কি মুত, চরি মদ পাওয়া যায়??? জফরফর ষার🍷🍷👻👻🚬🚬",1,celebrity
শয়তানের দাদা জাপর,1,celebrity
তোর গোফ তুলে তোর পিছনে সেট কইরা দিমু।  বান্দির পুত,1,celebrity
এই_কয়দিন কি 'হাগু' কষা হয়ছিলো.??😜 হঠাৎ 'পুন্দানী' খাইতে আইলা কেন..??😂,1,celebrity
আমি এখানে অসংখ্য গর্ভবতী ভাইদের দেখতে পাইতেছি। ভাইয়েরা নিজের খেয়াল রাখেন। অকারনে হাসাহাসি এই অবস্থায় আপনাদের জন্য ক্ষতিকর,1,celebrity
হালার পুত মরেনি?,1,celebrity
চুদছে,1,celebrity
#গেবনের শেষে আইসা আপনার মুখোশ টা খুলছে এতেই আমি মহাখুশী ✌✌আপনি তো হ র হ র করে বমি করবেন নাকি আমাদের দেখলে👿 আমরা না হয় মূত্রত্যাগেই আপনাকে দিব #গু দক্ষিনা,1,celebrity
এই লোকটা শিওর মাদার**। এই ইতরটা মাদার** না হয়ে পারেই না।,1,celebrity
তোর মতো গাজাখোর এর লেখ পড়ার টাইম নাইক্কা 😕😕,1,celebrity
চু★দার টাইম নাই...,1,celebrity
শুয়োরের বাচ্চাগুলা চলে এসেছে comment section এ লেদাইতে। জন্মের দোষ থাকলে যা হয়........,1,celebrity
"৫ জি গতিতে কমেন্ট পড়তে যাইয়া  আমার ত মাথা ঘুইরা হড়হড় করে বমি আসছে, ষাঁড় 😂😂",1,celebrity
আপনি তার হোগার বালটা ছিঁড়বেন,1,celebrity
হালার্পোরে কেউ গরম ডিম থেরাপি দেও। ডিম আমার পক্ষ থেকে।,1,celebrity
You bustard,1,celebrity
"কুত্তার বাচ্ছা জাপর, কমেন্ট গুলা পড়",1,celebrity
আমি যখন আগু করি তখন আপনার মতো চেতনা  দের কথা মনে পড়ে ঠিক মতো আগু করতেও পাড়ি না হালা গাজা খুর,1,celebrity
কুকুরের জীবনী পড়ে যে টুকু সময় ব্যায় হলো আমার জীবনে মনে হয় এই প্রথম  ডাস্টবিনে মুল্যবান   সময়টা ফেলে দিলাম ।,1,celebrity
আমি মিরজাপর দেখি নাই তবে তোর মতো একটা ***** পুএরে দেখছি হ্লা নাস্তিক😒😒 তোকে অনেক লাভ করতাম অনেক বড় ফ্যান ছিলাম তোর বাট আজথেকে তোকে বয়কট করলাম😁,1,celebrity
চেতনার মরিচ কি স্যার এর পু*কিতে ও ডলে দেওয়া হইছে??,1,celebrity
বাঙ্গালিরে অনেক বোকাচোদা বানাইচো হ্লার পো হ্লা😭😭,1,celebrity
তুই জারজ,1,celebrity
চুদির ছেলে গল্প লিখতে পারো সেই ১ তারিখ থেকে আর আজকে ৩ তারিখ আর ছাত্রদের এই সুষ্ঠ এবং মানবিক অধিকার আদায়ের আন্দোলন এ এতটুকু কি তাদের কাছে এসে একত্ব জানাতে পারতেন না?,1,celebrity
"খুনি ধর্ষন, গোলাম আযম, নিজামী, সাইদী রাজাকারদের চোদনে এতিমের টাকা চোর খালেদার ওরজে জন্ম পতিতালয়ের সন্তান গুলো এখানে হাহাহা রিয়েক্ট্য ও বাজে কমেন্ট করছে..",1,celebrity
এই খান★র পোলায় কোন দিন মানুষ হইবো না,1,celebrity
তুমি এত কিউট কেন গো বাইঞ্চোদ?,1,celebrity
">> অভিজিৎ রায়ের স্বরুপ আড়ালের চেষ্টা কেন <<  ১)___প্রচার হচ্ছে অভিজিৎ ছিল বিজ্ঞান লেখক, কিন্তু কুত্তার বাচ্চা যে চটি লিখত সেটা আড়াল করা হচ্ছে। , ২)___প্রচার হচ্ছে অভিজিৎ ছিল প্রকৌশলী, কিন্তু শুয়রের বাচ্চা যে নাস্তিকদের গুরু ছিল সেটা কেউ তুলে ধরছে না।  , ৩)___প্রচার হচ্ছে অভিজিৎ ছিল মুক্তমনা, কিন্তু কুত্তার বাচ্চা যে আমাদের ইসলাম, আল্লাহ, ও রাসুল (সাঃ) কে নিয়ে মারাত্মক কুটুক্তি করত সেটা আড়াল করা হচ্ছে।  , ৪)___প্রচার হচ্ছে অভিজিৎ হত্যা জংগীদের কাজ,কিন্তু লেখনীর মাধ্যমে শত শত নাস্তিক তৈরী করা যে এই শুয়রের বাচ্চার কাজ ছিল সেটা এড়িয়ে যাওয়া হচ্ছে। ,,, -------------- কেন এই লুকোচুরী? কি উদ্দেশ্যে মিডিয়া আর কুত্তালীগ এই সব জ্বলন্ত সত্যকে আড়াল করছে? নাকি তলে তলে নাস্তিকবাদী সম্রাজ্য কায়েমের চেষ্টা করছে এই সব কুত্তার বাচ্চারা? যেই উদ্দেশ্য থাকুক না কেন , ওলীদের এই জমিনে কোন কুত্তার বাচ্চা নাস্তিকতার প্রচারে এগিয়ে আসলে তাকে থাবা বাবা আর অভিজিৎ এর পরিণতি বরণ করতে হবে।   বি : দ্র : ইসলাম বিদ্বেষীদের কোরানের পরিভাষায় জানোয়ারদের সাথে তুলনা করা হয়েছে। এদের ব্যাপারে কুত্তার বাচ্চা, শুয়রের বাচ্চা এই জাতীয় শব্দ ব্যাবহারে সমস্যা নেই ৷৷৷৷",1,celebrity
হালারে ফাটা বাঁশ দে,1,celebrity
জাফর ইকবাল স্যার তো বমি করার কথা বলেছে আমিতো  প্রস্রাব করে দেবো এই কুলাঙ্গার রাজাকার বাচ্চাদের মুখে।,1,celebrity
"এতো গ্লানি আপনার আসে কৈ থেকে? গ্লানির চোদনে বমি কইরা দেন নাকি? তবে যাই হোক চাটতে কিন্তু আপনি খুব ভার পারেন, ঘুরিয়ে ঘুরিয়ে, ইনিয়ে বিনিয়ে ওই একটা পায়ই চাটতে। চাটেন ভাল করে চাটেন।",1,celebrity
"""ভূতের বাচ্চা সোলাইমান""-থিকা অনুপ্রাণিত হোয়া লিখতাম ""রাজাকারের বাচ্চা জাফর""! স্যার,লিখুম?",1,celebrity
এই ষাঁড়ের বিপরীতে বা তাকে নিয়ে কিচ্ছু বলতেই বিবেকে বাঁধে আমার!   এ কি মান+হুঁশ এর পর্যায়ে পরে কিনা আমার জানা নাই।  কোন মানদণ্ড থাকলে কেউ জানাবেন। মেপে দেখবো সরকার আমার মান কতটুকু বাকী রেখেছে। তারপর এরটা মাপবো।,1,celebrity
"হ্লা এবার যদি না মরচে আমি গুয়ামাইরা তুরে মারিফালামু, একবার রাম ঠাপ খাইলেই ওপারে গিয়ে ভাল থাকবি মাগির পুত",1,celebrity
"তুই একটা খানকির পোয়া, আর তো মা একটা খানকি আছিল (কপি)",1,celebrity
একটা আস্ত শুয়োর,1,celebrity
"হিন্দুরা মূর্তিপূজা করে,তাই তারা একটা গন্ডমূর্খ' ।দুঃখিত।আমি মুক্তমনা,তাই মুক্তবুদ্ধির চর্চা করতেছি।কিছু মনে করবেননা।",1,celebrity
"তোরে পাবলিক পুটকি মারতে মারতে, পুটকির ফুটা এতো বড় করে ফেলেছে যে,এখন আর টের পাসনা পুটকি দিয়া বাঁশই দেয় না পদ্ধা সেতুর পিলার!",1,celebrity
বাইঞ্চুদ হা-জি-র!😜,1,celebrity
আচুদা হালারপুত,1,celebrity
জাফ্রাকিবালের মুখে হাগু করি...,1,celebrity
এইগুলা সব ছাগুদের কারবার :v,1,celebrity
"হালকা মুতে শুয়ে পরুন,,সুশীলসমাজের গুষ্ঠিচুদি",1,celebrity
তুই নাস্তিক তুই কুকুর তুই হারাম জাদা তুই জারজ তুই আওয়ামী লীগ তুই ভারতের দালাল তুই একটা জানোয়ার।।।।।।,1,celebrity
19 bosorer zubok hoye muktuzuddher somoy gorte lukiye thako...abr ekhon abr muktuzuddher chetona chudau... Sala nastik kuthakar,1,celebrity
এখানে জাফরী ছাগু দ্বারা ভরপুর... শুয়োর ছানা গুলা সারাজীবন গু ই খেয়ে যেতে চায়।,1,celebrity
আমি বাইনচোদ দেখেনি। আপনাকে দেখেছি।,1,celebrity
"এক বালতি বমি,চু*****রানী।",1,celebrity
ঐ নাস্তিকের বাচ্চারে জবাই করে মাথা দিয়ে ফুটবল খেলবো।তারপর বুজবে হালায়,1,celebrity
জাতীয় শুয়োর,1,celebrity
"জাফর ইকবাল মানে ১ বালতি দুধের মধ্যে ১ ফোটা গো-মূত্র।  (চেতনা বাদীরা কোথায়,,, ধরিয়ে দাও আমাকে)",1,celebrity
"আরেক শ্রেণির বাঞ্চোত আছে। এরা পরেছে জাফর ইকবাল এর পিছনে। কোটা আন্দোলনের লেখাটির আগ পর্যন্ত আমরা দেখতাম যে, জাফর স্যারে আসলে কাদের জ্বলে। ৯৯% জ্বলতো শিবিরের, ০.৮% জ্বলতো বিএনপির। আর ০.২% জ্বলতো স্থানীয় আওয়ামীলীগ ও ছাত্রলীগ এর। জাফর ইকবাল যখন এই দেশের শিশু কিশোরদের এডভেঞ্চার বইগুলোর মাধ্যমে অন্যায়ের বিরুদ্ধে দাঁড়ানোর জন্য প্রস্তুত করেছে, তুমি বাঞ্চোত তখন শিবিরের কিশোর কণ্ঠ পড়তা। জাফর ইকবাল যখন বিএনপি-জামাতের আমলে গল্পের মাধ্যমে শিশু-কিশোরদের বুকের মধ্যে মুক্তিযুদ্ধের আগুন জ্বালিয়েছে, তুমি বাঞ্চোত তখন শফিক রেহমানের যায় যায় দিন পড়তা আর মুঠো মারতা। সাস্টে দিনের পর দিন ছাত্রলীগের সন্ত্রাসী হামলা নিয়ে জাফর ইকবাল লিখছে, তোমরা আঙ্গুল চুষছো। যার কারণে তারে না পারে সেখানকার শিবির দেখতে, না পারে ছাত্রলীগ। আর তুমি বাঞ্চোত আজকে আলুপোড়া খাইতে আসছো? বিশ্বজিৎ হত্যাকান্ডের সময় ছাত্রলীগকে নিয়া 'বিশ্বজিতের লাল শার্ট' কেডা লিখছিলো? তুমি? প্রশ্নফাস নিয়ে যখন সর্বস্তরের বুদ্ধিজীবীরা মুখে ইয়েটা ভরে বসে ছিলো, তখন বছরের পর বছর সরকারকে, নুরুল ইসলাম নাহিদকে কে 'বিব্রত' করছে? তুমি? তাকে বিব্রত করবার অপরাধে জেলে পুরবার ভয় পর্যন্ত দেখাইছে এই নাহিদ, আর আজকে তুমি জাফর ইকবাল দালাল - এই মন্ত্র সুদাও? তুমি যখন ভাত খায়া, খেচে আরামের ঘুম সুদাইসো, জাফর ইকবালদের বাড়িতে তখন বোমা মারছে, আগুন দিছে। তুমি এখন বিশাল কমরেড হইছো, না? যখন তোমার স্বার্থে আঘাত লাগছে, তখন জাফর ইকবাল হয়া গেছে দালাল, আর তুমি ফেসবুকে ইশট্যাটাশ মেরে বিশাল বিপ্লবী! তুমি শাহবাগের বুকে দাঁড়ায়া বুকে গালে পিঠে নিজেকে রাজাকারের বাচ্চা বইলা পরিচয় দিবা, আর একজন শহীদ সন্তানের গায়ে লাগতে পারবে না? তারা ভাইসা আসছে, না? পোস্টারে, ব্যানারে মুক্তিযোদ্ধাগো নিয়া ট্রল করবে, আর শহীদ সন্তান হয়া তিনি মুখে আঙ্গুল ঢুকায়ে বইসা থাকবে, না? তিনি আন্দোলনের সাথে জড়িত সবাইকে কি কটাক্ষ করছিলো? তাইলে তুমি যদি তাদের একজন না হয়া থাকো তো তোমার এতো জ্বলে কেন? তোমাদের এতো অপছন্দের লোক সে, তাইলে তারে খুঁজো ক্যান সব ক্ষেত্রে বাঞ্চোতের দল? জাফর ইকবালে কাদের জ্বলে, কাদের চুলকায় সে আমরা জানি, তবে কিছু গাধার বাচ্চা যে না বুইঝা তাদের সাথে ফাল পারে, তাদের যখন বলি শিবিরের ট্র‍্যাপে পা দিস না, তখন তারা ন্যাকা ন্যাকা হয়ে বলবে, 'হুহ! আছেই ত আপনাদের ঐ একটা অস্ত্র, শিবির শিবির'। '' -- Nishom Sarkar",1,celebrity
জানোয়ার এটা কোটা বিরোধী আন্দোলন নয় কোটা সংস্কার আন্দোলন।,1,celebrity
"হালা শুয়োরের বাচ্ছা জাফর দালালি বাদ দে,সাধে কি ছাত্রদের হাতে পেদানি খাস।",1,celebrity
"।। জবর ইকবাল তুমি আমার বালের টিচার।। তোর রিয়েল ক্যারেক্টার সবাই জানে। এখন বলছিস আ:লীগের কথা। আর বি.এন.পি ক্ষমতায় থাকতে কইছস তাদের কথা। শালা টাকার ধান্দা করছ, সবাই তা বুঝে। তুই কিসের বুদ্ধিজীবীরে শালা বাঞ্চত। আ:লীগের ক্ষতি করছ উল্টা পাল্টা কথা কইয়া।",1,celebrity
"ছাগল জাফ্রিকবালের কাছে প্রশ্ন, কেন রাজাকার শব্দ টা ছাত্রসমাজ বরণ করছে????কই এতো লিখলেন  মুতিয়া কে নিয়ে তো কিছুই বললেন না। বলবেনই বা কেন? আপনি তো দআকার দালাল।",1,celebrity
খান্কির পোলা তুই একটা মাসুদা ভাট্টি,1,celebrity
"ওরে চুতমারানি , সিফাত কাকা তোরে দিয়া ব্লোজব করানোর জন্য খুজতেছে , এই বার পাইলে তোরে প্রেগনেন্ট করে ছাড়বে ।",1,celebrity
"তোমারে চুদিনা, তোমার মেয়েকেও চুদিনা। তুমি চুদো তোমার মেয়েকে আর।  এটা কিন্তু সায়েন্স ফিকশন ছিলো, ভুলেও কমেন্ট ভাবিয়েন না। আর ভাবলে আমি হড় হড় করে আমার বীর্য ঢেলে দিবো ওর বউয়ের ভোদায়।",1,celebrity
অতি বর্ষনের ফলে ট্রেঞ্চের উপর থিকা মাটি সরে গেছে। টেটাস মাইরা আবার গাতায় থুক্কু ট্রেঞ্চে হান্দাই যাবে...,1,celebrity
জ তে জাফর তুই দালাল তুই দালাল,1,celebrity
স্যার আপনি একটা বোকাচোদা জানেন? :|,1,celebrity
জ তে জাফর ।তুই রাজাকার তুই রাজাকার !,1,celebrity
তুই মাগিরপুত লুইচ্যা,1,celebrity
লুইচ্চা মাদার ফাকার তোর আসল রুপ পোলাপান বুঝতে শিখছে।,1,celebrity
"গর্দভের বাচ্চা সমার্থক শব্দ কাকে বলে, সেটাই জানেনা।খচ্চর কোথাকার !!!!",1,celebrity
ছাগলের বাচ্ছারা সব জায়গায় কাঠাল পাতার স্বাদ নিতে চায়।পাকিস্তানের ফেলে যাওয়া উচ্ছিষ্ট এরা কোন সন্দেহ নাই। আপনি এগিয়ে যান স্যার এইসব পরিচয়হীন দের আব্লামী তে কিছু যায় আসেনা,1,celebrity
চটি গল্পটা পড়া শেষ করে হাত মার্তেছি ৷,1,celebrity
"নডির পোলা চুপ থাক,,!",1,celebrity
"নডিরপুত🐸🐸 কমেন্টে আয়, রেণ্ডীমাগিরপুত।🐸🐸",1,celebrity
"ষাড় নাস্তিক, দালাল ও সরি কোদাল ইকবাল এতদিন কোথায় ছিলেন???",1,celebrity
"আপনি খুব বাজে ধরনের একজন লুইচ্চা, না ঘরের, না ঘাটের। হিজরা টাইপ আপনি।",1,celebrity
কি মিয়া আবালচোদা কথা কও কেন😜,1,celebrity
জাফর ইকবাল স্যারের মতো আমিও মুখে আঙ্গুল দিয়ে বমি করব সেসব কুলাঙ্গারদের উপর যারা নিজেদের গায়ে আমি রাজাকার লিখে রাজপথে দাঁড়িয়েছিল,1,celebrity
পাগল চুদতে আইলাম।,1,celebrity
চোদনা কোথাকার.....নিজেকে খুব বড় বোকাচোদা মনে করেন তাই না 😂😂😂,1,celebrity
"কতগুলো আবালের কমেন্টেস পড়লে মনে হয় এদের জন্মে পাকিদের বির্জ ব্যবহৃত হইছে, তাই এ বেজন্মাগুল না পড়ে বাজে কমেন্টস করে,",1,celebrity
জাফর ষাঁড় আমি আপনার ইয়া বড় ভক্ত।,1,celebrity
কুত্তার বাচ্চা। দালাল কোথাকার।,1,celebrity
বাইঞ্চদ তর এসব জাইনা লাভ নাই।।,1,celebrity
ফইন্নির ঘরের ফইন্নির কতা হুনছৎ,1,celebrity
বালের ইকবাল,1,celebrity
"জাফর স্যার তো দেশের প্রথম সারির লুইচ্চা সারাদিন মেয়েদের বিছানায় পরেই থাকে,,,আর রেন্ডিয়ার কুত্তাদের দালালি করে",1,celebrity
"বেশ্যামাগী আর বেশ্যা মরদদের কথাগুলো পড়ে মনে হচ্ছে এদেরকে রাজনৈতিক দল আর দলের নেতারায় মুখে তুলে ভাত খাওয়ায়ে দেয়!  বেশ্যাপনা আর দালালিপণা ছাড়েন- দেশের আইন কানুন ঠিক করুন- জনগণের জানমালের হেফাযত কিভাবে হবে সেটা ভাবুন- বালের গণতন্ত্র, রাজনীতি, রাজনৈতিক দল এগুলো থেকে বেরিয়ে এসে নিজ নিজ পেটের ভাতের কথা চিন্তা করুন! Please  এদেশের পুটকি মারা গেছে- জাহান্নামে যাক দেশ জাহান্নামে যাক রাজনৈতিকদল আপনি আপনার কাজ কাম করেন,পরিপার পরিজন নিয়ে দু-বেলা খেয়ে পড়ে বাঁচেন!",1,celebrity
এই সবাই ষাঁড়কে মাথায় হাত বুলিয়ে দাও।,1,celebrity
খানকির পোলা দালালি চুদাস,1,celebrity
সালারপুত,1,celebrity
চুদলাম না তোমার ভালোবাসা।,1,celebrity
শালার পো কখন ফেসবুতে পোস্ট দিলি আর শেষে লিখলি ১ তারিখ! ল্যাংটা কইরা পিডামু তোরে!,1,celebrity
জনম জনম থাকে পাশে ভুলনা।  হালা গাড়িয়া,1,celebrity
অদভুদ এক বইশ্যাজীবির নাম ছ্যার জাফর... বড়ই অদভুদ এই ছ্যার,1,celebrity
"হ্যারে বাড়া তুই তো রাজাকার ,গাথার ভেতর যখন তোরে কইচিল পোঁদ মারতে চাইছিল তখন তুই তো পোঁদ মারিয়েই রাজাকার দলে যোগ দিছিলি রে বাড়া",1,celebrity
"ছাত্ররা না হয় ভুল করে আমি রাজাকার লিখাটি লিখছে। কিন্তু বমি মন্ত্রী আদো কি জানেন আমি রাজাকার লিখাটি একটা সাহিত্যিক প্রতিবাদ??? ছাত্ররা আমি রাজকার লিখছে আর আপনি সেটাকে ঘুড়িয়ে,পেচিয়ে, উল্টায়ে, বল্টায়ে পেট বাচ্ছে (গ্রামের ভাষায়) বলে দিনের পর দিন চালিয়ে দিচ্ছেন। ছাত্ররা যৌক্তিক আন্দোলন নিয়ে প্রতিবাদ করলে পেট বাজে আর আপনি দালালি করতে হয় টিউমার। কুসসুম্মান বমি মন্ত্রী জাতু।",1,celebrity
এ সব নাটক করে মানুষকে ধোকা দিতে পারবেন না।এ সরকারের সময়ই একমাত্র জালিয়াতি হয় শিক্ষা ক্ষেত্রে এটা দেশবাসি ভালই জানে।আর আপনি যে একটা পাককা শয়তান।এটাও মানুষ ভাল জানে।,1,celebrity
তোমার মত বেশ্যার খদ্দরের কারণে এসব ঘটে।।।,1,celebrity
"বালের দালাল, এক কঠিন ভাদা..",1,celebrity
"র্ষাড় আপনার লজ্জা লাগেনা, দেখুন কমেন্ট গুলো পড়ুন, আপনাকে কি বাঁশ টা দিয়েছে,",1,celebrity
"৩০ হাজার ভুয়া মুক্তিযোদ্ধার ব্যাপারে কিছু বলতেন,,,,,এতো যখন বোঝেন,,,,!!! মাইয়াডারে বিয়া দিছেন এক্ষান বিদেশি ইহুদি নাসারার লগে,,,,ক্যা এত্তো দেশ প্রেম তয় এক্ষান দেশি পোলার লগে বিয়া দিতেন,,,   এ মুখে মুখে খালি এদেশের তরুন প্রজন্ম,,,আহা আহা খালি ভাওতাবাজি",1,celebrity
"ওরে শুয়ার, লজ্জাও হারাইছিস!",1,celebrity
আবাল,1,celebrity
মুক্ত মনার নামে দালালি চোদান বালের ।  এইটা আমরা বুঝি।,1,celebrity
এই মাদারী দেখি সত্যি সত্যিই মদ খেয়ে হর হর করে দিলো 🔞🎃,1,celebrity
"চুতিয়া চৌধুরী যখন সাধারণ ছাত্রদের রাজাকার বলে ভুষিত করলো তখন আপনার এই সুশীলতা কোথায় হাওয়া খেতে গিয়েছিল? আমি রাজাকার লেখার পেছনের কারন টা জেনে কথা বললে ভাল হতো।অল্প বিদ্যা ভয়ংকরী বলে একটা কথা আছে, এটা তো জানারই কথা আপনার।আর সবাইকে মুক্তিযুদ্ধ বিরোধী বানায় দেন ঢালাও ভাবে। :) খুবই সুন্দর কথা।আপনি কি জানেন বাংলাদেশের মুক্তিযুদ্ধে ১৩ বছর বয়সী এক ছেলেও যুদ্ধে গিয়ে জীবন দিয়েছিল? আপনি ১৯ বছরের দামড়া হয়ে কোন চুল টা ছিড়েছিলেন তখন? সম্মান হারাবেন না।একবার হারালে আর তা ফেরত পাবেন না।বায়াসড লেখা অফ করেন।কোটা বাতিলের দাবীও কেউ করে নাই, মুক্তিযুদ্ধের বিরোধিতাও করে নাই।দালালি বন্ধ করুন।",1,celebrity
"আপ্নেরে চুতিয়ার ভাবতাম, এখন সাউয়া মনে হয়।",1,celebrity
"তুই রাজাকারের বাচ্চা মন্তব্য যখন পড়িস না, তোরে স্ট্যাটাস চুদাইতে কয় কেডে! মন্তব্যগুলো পড়ে দেখ, কি রকম ঘৃণাভরা চোখে তোরে মানুষ দেখে সেটা টের পাবি।",1,celebrity
মাদারচোদের বাচ্চা খাংকির পুলা তরে পাইয়া লই কোনোদিন,1,celebrity
আর নিজের চক্রায় তেক দে।তোর চোর বাটপার এ ভরা। আবার জামাত শিবির লইয়া মরছ সালা কুকুরের বাচ্চা  আজকেও তো একজন মারা গেলো কুত্তালীগ এর কি করসত তাদের জন্য,1,celebrity
"জারজ শিবির আর বিএনপি ছাগলের দল এরা রাজপথে স্থান না পেয়ে, দেশে মানুষ ও বিদেশী বন্ধুদের কাছে স্থান না পেয়ে, ফেইসবুকে কে নামে বেনামে ফেইক আইডি খুলে গুজব মিথ্যাচার আর গালিবাজি করে.. এরা পাকি বীর্যের কিট পতিতাতলে জন্ম এদের জারজ গুলো . ১৯৭১ সালে জেনারেল নিয়াজী আর জাঞ্জুয়ানদের দেওয়া পাকি বীর্যের কিট গুলো এখন ও স্বাধীন বাংলাদেশে , জারজ শিবির আর ছাগলের দল বিএনপি বেশে লুকিয়ে আছে.. এরা রাজপথে আন্দোলন এর ব্যার্থ হয়ে বিদেশী সমর্থন ও দেশের মানুষ এর সমর্থন না পেয় আজ পাগলে রুপ নিয়েছে.. এরা আজ ফেইসবুকে ফেইক আইডি খুলে নামে বে নামে আইডি খুলে গুজব মিথ্যাচার আর গালিবাজি করে.. খুনি ধর্ষক নিজামী,সাইদী,গোলাম আযম রাজাকারদের চোদনে , এতিমের টাকা চোর খালেদা জিয়ার পেটে জন্ম নেওয়া কিট গুলো ই নেগেটিভ আর হাহাহা করে..",1,celebrity
এটা পোষ্ট না এক জ্ঞান মূর্খ কুকুরের ঘেউঘেউ,1,celebrity
"ওরে শয়তানের খালাতো ভাই, শফি সাবকে নিয়ে উল্টাপাল্টা বলিস??? ব্যাটা বদের বাচ্চা বদ, সেই ঠিক, একবার মরে দেখ, তোর লুইচ্চামি কই যায়। প্রাইমারী পর্যন্ত পড়ে মেয়েরা পর্দা করে ঘরে বসে গেলে তো আর তাদের নিয়ে ডিজে পার্টি করতে পারবি না, এই জন্যই তোর গা জ্বালা শুরু হইছে। চিন্তা করিস না, তোর মত কিছু কীট-নারী থাকবেই। আর গামছা দিয়ে সে যে কয়জন নারীকে পদ্মা থেকে ছেকে রাখতে পারবে, তারাই নেককার নারী। বাকী সব তোর বউ আর তোর মেয়ের মতই......শয়তানের ওস্তাদ। কত বড় সাহস শফি সাবকে নিয়ে কথা বলে।",1,celebrity
চৌদনা কি কমেন্ট গুলা পরেনা??,1,celebrity
তুই হালা জুকারকে হার মানাতে পারিস সাউয়ার পোলা .. সুদির ভাই..,1,celebrity
"কিরে মাদাচোদ চেতনা ব্যবসায়ি, এখন কিছু বলিস না কেন?  তোর নানির মাইয়ারে চুদি খানকির পুত",1,celebrity
জাফর ইকবাল মানে ১ বালতি দুধের মধ্যে ১ ফোটা গো-মূত্র।,1,celebrity
আপনার মতো পা চাটা কুকুররা শান্ত থাকেন দেশে শান্তি থাকবে,1,celebrity
তুরে যে কেমনে স্যার ডাকে বুঝিনা! তুইতো মাগির দালাল হবার কথা.,1,celebrity
তুরে চুদে,1,celebrity
৭ই মার্চের ভাষণে ষাড়ের চেতনা জাগ্রত হলেও তিনি গর্তে লুকিয়ে ছিলেন কারন মুরগির কলিজা হওয়ায় তিনি যুদ্ধে যেতে পারেননি।,1,celebrity
"এই শালার্পুত, তুই ৭১ এ কই ছিলি??",1,celebrity
তুই বান্দির পুয়া,1,celebrity
বদমাইশ টা তাহলে মরে নাই! পুরো লেখাটা স্ববিরোধীতা  অার অাত্মপ্রতারনায় ভরপুর!!,1,celebrity
আপনি যে একটা 'চুদির বাই' জানেন সেটা? 💀,1,celebrity
তুই একটা বোকা চোদা,1,celebrity
চুদলাম না তুর মোটিভেশন.....,1,celebrity
"শুয়োরের বাচ্চাগুলার কাজ নাই, comment section এ লেদাইতে আসে",1,celebrity
এই আলা চুদানির পুত খানকিরপুত মাগির পুত! এতদিন কি তোর মাগী মা শেক্স হাসুনার সোনার ভিতর ঢুকে আছিলি?এখন কাহিনি চুদাওতে আসছস।ভরে দিবো একদম ডান্ডা,1,celebrity
চুতিয়া যে রাজাকারের বাচ্চা বলে গালি দিয়েছিল এটা লিখেন নাই কেন? এটা বলার আগে কি আমি রাজাকার লিখে বুঝে ঝুলাইছিল?   অন্যের পা না চাইটা গু এর উপ্রে চাটা দেন।   অন্যের পা তো ভবিষ্যতে নাও থাকতে পারে। তখন কিসে চাটা দেবেন? গু সবসময় পাইবেন।গু  অলওয়েজ এবেইলেবেল । বিশ্বের যেখানে যাইবেন সেখানেই পাইবেন।,1,celebrity
"৭১ এর গত্তো জাফর, ২০১৮ তে মীর জাফর!!",1,celebrity
এই বোকাচোদা তো দেখছি ইতিহাস সমন্ধে একেবারে অঙ্গ ।,1,celebrity
"ওই শুয়র তোর মাতো তোকে জন্ম দিয়েই ভুল করেছে। এই বাংলার ভাগ্য ভালো যে তোকে কবরে শুইয়ে দিয়েছে, ভালো থাক তুই পরকালে।",1,celebrity
নোয়াখালী বিভাগ চাই ষাঁড়,1,celebrity
আপনার মতো পশুর কথায় কান দেয় কে??,1,celebrity
ছাগুদের কমেন্ট পড়তে আসলাম। ;p (৩),1,celebrity
বাইঞ্চোদ তোরে যাতে আর কোনদিন শিশু কিশোর দের জন্য বই লিখতে না দেখি।  পোলাপাইন তিনদিন আমাদের জনগনের সার্থে রাস্তায় আন্দোলনে নামছে। তুই বাইঞ্চোদ আজকে  আইছোছ মায়াকান্না চোদাইতে।,1,celebrity
হালা ফাউল এর বাচ্ছা!!,1,celebrity
একটি বিরল প্রজাতির গাঁড়'ল তার পোঁদ খাটিয়ে পোঁদ ঘামিয়ে এই পোস্টটা তৈরি করেছেন। সবাই গাঁড়াই বাবুর পোঁদে চরি পোস্টে লাভ্রিয়েক্ট দিন।,1,celebrity
ভূতের বাচ্চা জাফর ইকবাল স্যার আপনার প্রতি বিনম্র শ্রদ্ধা নিবেদন করছি......💩💩,1,celebrity
"হালায় লীগ_কানা, ফ্রীক_চোদা!!  And This bullshit ""তৈল_ইকবালীয়_রচনা"" is Enough to UNLIKE this কওমী_মাতা'র_ফাকার Page.... Keep Away Your Oily_Dumb_AssHole,  Muhammedzafariqbal Pak 😖",1,celebrity
ছার অাসলে সার না ছাগল!!!,1,celebrity
ষার একজন vvip মানে বুঝস? very very important person মদ খা মোরক্ষ চোদারা মদ খাবি মানুষ হবি শুঁটকি খাবি হড় হড় করে বমি করবি মোরক্ষ ছোদারা,1,celebrity
হালার পোয়াওআলা যখন তোদের আব্বা গণজাগরণ মঞ্জ শাহবাগে আন্দোলন করছিল তখন পাশে হাসপাতাল ছিলো তখন তো তুই নিজে গিয়ে সাফোর্ট করছিলি তখন কোথায় ছিল এত মানবতা,1,celebrity
বালের এক নাম জাফর,1,celebrity
স্যার আপনাকে চুদি স্যার,1,celebrity
টানা এ'কদিন প্রসব যন্ত্রনা সহ্য করে অতঃপর এইটা প্রসব করছেন ষ্যাঁর,1,celebrity
"#আপনার_মত_ছাগলের স্ট্যাটাস আমি এই পর্যন্ত পড়তে পারলাম যখন আপনি লিখলেন ছাত্ররা বুকে ""আমি রাজাকার"" লিখেছে।সেটা যে একটা নায্য আন্দোলনকারীদের যখন ""রাজাকারের বাচ্চা"" বলে গালি দিয়েছিল তার প্রতিবাদ ছিল, এটা বুঝেন না কিসের মাস্টারি করেন? ছাগলেও তো এর চেয়ে ভালো বুঝে। মুক্তিযোদ্ধা বা মুক্তিযুদ্ধের প্রতি অসম্মান কারও মনেই ছিল না,নেইও। আন্দোলনকারী সবাই বৈষম্যহীন সমাজ চেয়ে যে মুক্তিযুদ্ধ হয়েছিল, সেই চেতনায় বহন করেছিল। নিজে তো ছিলেন গর্তের মধ্যে।আমার বাবা,চাচারা মুক্তিযোদ্ধাদের বারুদ,গুলি বহন করেছে।দাদীরা ভাত রান্না করে খাইয়েছে মুক্তিদের।দেশটা শুধু অস্ত্র দিয়ে স্বাধীন হয়নি।দেশটা ভালোবাসা দিয়ে স্বাধীনতার সুখ পেয়েছে।",1,celebrity
"জারজ স্যর আপনি  গুজব ছড়াচ্ছেন,  স্যর আপনার গুজব কমিটির  সংগীরা  কৈ।",1,celebrity
"মদ খাবা আর জাফর ষাড়কে চোদবা...কেউ ঠেলাঠেলি করবেন না সিরিয়ালে দাড়ান,সবাই সুযোগ পাবেন",1,celebrity
"""জ"" তে জাফর ইকবাল, তুই রাজাকার, তুই রাজাকার....",1,celebrity
"you bloody bitch just get lost frm here,hw dare u!! Don't u think,u r nt comparable to his shoes??? @shanawz",1,celebrity
.....সুশীল জানোয়ার;,1,celebrity
বাইনচোদ দেখতে ইচ্ছে করলেই আপনাকে মনে পরে,1,celebrity
"ওয়াও এখানে অনেক জাফ্রিকবালের চুশীল মুরিদ আছে,চোদনার পোলা পুরাই গিরগিটি,এক হালা কমেন্ট সোদাইছে দুই সপ্তাহ পরপর কলাম লিখে,আর কোটা আন্দোলনের সময়, একদিন ব্যাবধানে তিনবার তিন ধরণের মন্তব্য কেমনে আসে? আওয়ামী,বিনএনপি,জামাত কোন খানকির পোলাগো সোদার টাইম নাই,পেটে পিঠে লাথ পড়লে এমন চুশীল বুদ্ধি বেশ্যা আর রাজনৈতিক পতিতা গো জনগণ চুদে মঙ্গলে পাঠাই দিতে পারে।😈😈😈",1,celebrity
#গুগলে #মাদরচোদ লিখে সার্চ করেছিলাম😷গুগল আমাকে এই পোষ্টদাতার আইডিতে নিয়ে এলো😱 কাহিনী বুঝলাম না😒,1,celebrity
ভূতের বাচ্চা জাফর ইকবাল,1,celebrity
আচোদা জাফ্রাকবাল।,1,celebrity
"জ তে জাফর, তুই রাজাকার তুই রাজাকার  হুমায়ুন আহমেদ লিখেছিলেন, ""১৬ ডিসেম্বর, ভোর। ১৯৭১। আমার বুক ধক ধক করছে। বাজিছে বুকে সুখের মতো ব্যথা। বিশ্বাসই হচ্ছে না, আমরা স্বাধীন। এখন আর মাথা উঁচু করে হাঁটতে সমস্যা নেই।… ‘নিজের দেশের মাটি/দবদবাইয়া হাঁটি।’ আমি দবদবিয়ে হাঁটার জন্যে বের হলাম। প্রথমে খুঁজে বের করতে হবে আমার ছোট ভাইকে (জাফর ইকবাল)। শুনেছি, সে যাত্রাবাড়ীতে আছে। গর্তে বাস করে। যাত্রাবাড়ীতে আমার দূরসম্পর্কের এক মামা বাড়ির পেছনে গর্ত করেছেন। তিনি তাঁর স্ত্রী এবং দুই ছেলে নিয়ে গর্তে বাস করেন। জাফর ইকবাল যুক্ত হয়েছে তাদের সঙ্গে।""  --কত না অশ্রুজল  (আমি রাজাকার  না)",1,celebrity
"জনাব জাফর ইকবাল!   আপনার এই লেখায় আপনি নির্লজ্জভাবে দালালী এবং চামচামি করেছেন। যার এতটুকু জ্ঞান নেই যে একজন ছাত্র কি কষ্ট নিয়ে তার গায়ে লিখলো আমি রাজাকার, কেন লিখলো এ কথা... সে কিনা আবার তা নিয়ে সমালোচনা করতে আসে।   যখন সংসদে দাঁড়িয়ে দেশের একজন মন্ত্রী এত ছাত্রকে রাজাকার বললো তখন তো আপনার গায়ে লাগেনি। নাকি তখন ৭১ এর মত গর্তে লুকিয়ে ছিলেন!?   আপনার মত এমন ভীতু, কাপুরুষ, নির্লজ্জ, পা চাটা চামচা নাকি এদেশের বুদ্ধিজীবী! ভাবতে আমাদের এখন ঘৃণা হচ্ছে। আপনি সামনে আসলে এখন আর আপনার সাথে ছবি উঠার রুচি আসবেনা, গলায় আঙুল ও দেয়া লাগবেনা আপনাকে দেখেই হর হর করে বমি চলে আসবে।",1,celebrity
বাড়া তোমার ঘুম ভাংছে,1,celebrity
বাংলাদেশে ওনার মতে বিচিহীন লোকের প্রয়োজন নেই।,1,celebrity
জাফর এক বাল😃😃,1,celebrity
জাফর বুকাচুদা তুমি এই শেষলগ্নে আর পোস্ট চোদাইতে আসিও না _তোমার পোস্ট দেখলেই তোমারে থাবড়ানি দিতে মন চাই।।,1,celebrity
"ছি, আপনাকে বাচ্চাকালে অনেক সম্মানের চোখে দেখতাম, কিন্তু যখন বুঝতে পেরেছি আপনি একটা মেরুদণ্ডহীন, পাচাটা দালাল সেদিন থেকে আপনার মুখে হড়হড় করে বমি করতে ইচ্ছা করে।",1,celebrity
এই হল নাস্তিক চুদিশীল সমাজ!!,1,celebrity
ভূতের মুখে রাম নাম 😂😂😂 আচুদা,1,celebrity
জাফর ইকবাল  একটা মাদারচোদ,1,celebrity
এই হারামি একটা দালাল।দালাল তো দালালের মতই কথা বলবে।,1,celebrity
তোকে কুওা দিয়ে চোদাবো -সিফাত উল্লাহ,1,celebrity
"তুমি জাতীয় চুতিয়া, দালাল",1,celebrity
আমি রাজাকার দেখেনি আপনাকে দেখেছি  রাজাকার,1,celebrity
", , স্যার আপনার লেখা দেখলে এখন হড়হড় করে বমি আসে,,,, কিছু মনে করবেন না, এইটা আপনার কাছ থেকে শিখেছি,,,, ,",1,celebrity
তুই হইলি আসল খানকির পোলা,1,celebrity
ফাডারপু ফাডা' তোমার লজ্জা শরম  কিছু থাকা উচিত। তোমারে ত বর্তমানে বাংলার জনগণ চুদতে চাইনা তারপরও কেন অসময়ে দালালি করতে আসো ??,1,celebrity
তোর পুটকি তুই মার।।,1,celebrity
"মদ খা হারামজাদা, মদ যদি না খেতে পারিস তাহলে শুঁটকি খেয়ে পেত্নী চু......…!",1,celebrity
"_ দেশের কয়েকজন কুলাঙগারের মধ্যে জাফর ইকবাল একজন , আ'লীগের দালাল|",1,celebrity
২০১৮'র সবচেয়ে বড় রাজাকার #আপনি !!!,1,celebrity
"""""জাফর একটা ৰুকাচূদা""""",1,celebrity
"আপনি হলেন জাতীয় মুনাফিক, জাতীয় বেইমান।আর আপনার মত মানুষ গুলো বুদ্ধিজীবি না,আমার মনে হয় আপনারা বুদ্ধিযোগি!!!!",1,celebrity
গাফর ইকবাল সারকে সুদেচেরে,1,celebrity
"পাগল ছাগল তুমি, প্রতিনিয়তই তোমার মুখে, মানুষ করে বমি:- তোমার মতো সুবিধাবাদী, চেতনার জমিনে হচ্ছে আবাদি; তুমিহীনে চেতনা, কল্পনা করা যায় না, তোমার চেছরামিতে, আমরা বহুকাল হয়েছি আকাল, ভুলে যেনো ষাঁড় সময় বড়ই আকাল।।",1,celebrity
"ছাগুদের পাছায় জ্বলা শুরু হয়েছে, কমেন্টবক্সেই এদের যত বিপ্লব😂। ছাগুরা পেভিসন মলম কিনে আসিফ নজ্রুলের কাছে চলে যাও",1,celebrity
তুমি বোকাচোদা,1,celebrity
জাফর চোদার টাইম নাই,1,celebrity
"কিরে মাগীর পুলা,,,, তর মায়ের গোয়া থেকে বের হলি কেন,,,  চোদা হবে তর বউয়েরে। কাংখির পুলা তরা নাকি বুদ্ধী ব্যাশা,,,,তর মার হরডা",1,celebrity
"জনাব জাফর ষার,অতি অসম্যানের সাথে জানাচ্ছি, অাপনি একটা বানচোদ।",1,celebrity
"ওহে দালাল, ধানের শীষে ভোট দেওয়ায় ধর্ষকলীগ কর্তৃক নোয়াখালীতে গৃহবধু গনধর্ষীত হওয়ায় আপনার চেতনা জাগ্রত হয়না?",1,celebrity
মাদার চোদ তুই বাংলার কুলাঙ্গার,1,celebrity
"ছাগুদের কমেন্ট পড়তে আসছি, উর্বর মেধাবীদের দেখতে আসছি।",1,celebrity
স্যারের এতো ‘বাড়া’ লেখা পড়ে আমার শরীর শিহরিত হয়ে উঠলো।,1,celebrity
আচোদা খাইস্টা দালাল,1,celebrity
"জারজ শিবির আর বিএনপি ছাগলের দল এরা রাজপথে স্থান না পেয়ে, দেশে মানুষ ও বিদেশী বন্ধুদের কাছে স্থান না পেয়ে, ফেইসবুকে কে নামে বেনামে ফেইক আইডি খুলে গুজব মিথ্যাচার আর গালিবাজি করে.. এরা পাকি বীর্যের কিট পতিতাতলে জন্ম এদের জারজ গুলো কোন দিন আর বাংলাদেশে মাথা উচু করে বাঁচাতে পারবি না,, খুনি ধর্ষন, গোলাম আযম, নিজামী, সাইদী রাজাকারদের চোদনে এতিমের টাকা চোর খালেদার ওরজে জন্ম পতিতালয়ের সন্তান গুলো এখানে হাহাহা রিয়েক্ট্য ও বাজে কমেন্ট করছে..",1,celebrity
"অনেক শুয়োরেরা দেক্তেছি মুতিয়ার বক্তব্যকে ডিফেন্ড কর্তেছে! তো শুয়োরেরা তুমাদের দাবীনুযায়ী আম্রা নাহয় তার বক্তব্যের ভুল বুঝলাম, কিন্ত মুতিয়া কেন পরবর্তীতে আর তার বক্তব্য ক্লিয়ার করেনাই?",1,celebrity
চুতিয়া : চেতনা ব্যবসায়ী,1,celebrity
কিছু খানকির পুলার জন্ম হইছে সব জায়গায় হা হা রিয়েক্ট দেওয়ার জন্য। এসব শুয়োরের বাচ্চারা তাদের মা বইনের ধর্ষণের পোস্টেও হা হা রিয়েক্ট দিবে।,1,celebrity
খানকীর পোলা,1,celebrity
পা চাটা গোলাম মীর জাফর ।,1,celebrity
আরে ছাগলের বাচ্চা রাজাকারের পুত আল মাহমুদ নিয়ে কিছু লিখিস?,1,celebrity
"অপরাধী - জাফর ইকবাল ভার্সন :p === === === === ===  ﻿একটা সময় স্যার জাফররে সবই ভাবিতাম, তার বইগুলা সব যতন করে আগলাইয়া রাখতাম। তার গোঁফের নিচের হাসি দেইখা দুঃখ পুষাইতাম, স্যার বৃষ্টির নিচে কাঁদলে পরে হারাইয়া যাইতাম!  ওরে মনের খাঁচায় স্যার জাফররে দিয়াছিলাম ঠাঁই, এখন মোদের জন্য স্যারের মনে কোনো জায়গা নাই। ওরে হাতুড়ির ঘায় বাংলাদেশ আজ পঙ্গু হলো রে, এমন সময় স্যার আমাদের ফুটবল শেখায় রে!  ওরে ও জাফর স্যার, তুই অপরাধী রে! আমার কৈশরের সেই ভালোবাসা দে ফিরাইয়া দে! আমার আবেগ লইয়া পল্টি মারার অধিকার দিল কে?  স্যার তুই বড় অপরাধী, তোর ক্ষমা নাই রে!  স্যাররে স্কুল পলাই বই মেলাতে দেখিতে যাইতাম, আমি টিফিনের সব টাকা জমাই ফিকশন কিনিতাম। ওরে রাইতের পর রাইত জাগিয়া গল্প পড়িতাম, রাতুল-রুহান-রাশার সাথে হারাইয়া যাইতাম!  অহন দালালিতে পূর্ণ কলাম পড়ি ক্যামনে, যা পড়িলে হড়হড়াইয়া বমি আসে রে! স্যারের সুশীল বেশী ভণ্ড নীতি দেখলে মনে হয়, স্যার তো শুধু দলের এজেন্ট, মোদের কেউ নয়!  ওরে ও জাফর স্যার, তুই অপরাধী রে! আমার কৈশরের সেই ভালোবাসা দে ফিরাইয়া দে! আমার আবেগ লইয়া পল্টি মারার অধিকার দিল কে?  স্যার তুই বড় অপরাধী, তোর ক্ষমা নাই রে!  ---  Mozammel Hossain Toha",1,celebrity
শালার পুত সিলেট থাকি বাগ,1,celebrity
"এই হাউওয়ার পুত মরলে ও মানুষ হবেনা, এমনিতেই বিরক্ত এর উপর শ্লার বিরক্তিকর পোস্ট। 🖕🖕🖕🖕",1,celebrity
তর আম্মা যখন সংসদ বলছিলে রাজাকার বাচ্চা এই সময় তুই কঁই ছিল মাগির দালাল,1,celebrity
কমেন্ট পড়ে আমি চুদনা হয়ে গেলাম,1,celebrity
"ওরে বরাহ,  ওরে রাজাকার নাতি, ওরে রাজাকার পুত্র, তোর গনিত অলিম্পিয়াডের মতো লেখাতেও দালালি করতে হবে।",1,celebrity
ঠিক বলছেন ষাঁড়😆😆😆,1,celebrity
"হালায় মানভোদার ফাঁকে পড়ে আবোল তাবোল বকতাসে, চেতনাদন্ড সবে মাত্র খাড়া হইল। সামনে বহুত জনি সিন বাকি আছে....",1,celebrity
"জয় বাঙলা, নৌকা মার্কায় ভোট দিন। শেষে এই লেখাটা আশা করছিলাম শুয়োর😎",1,celebrity
"কেউ মাদারচোদ কে গালি দিবেন না দয়া করে, মুখ নষ্ট হয়ে যাবে😜😜😜",1,celebrity
আপনে হুমায়ূন আহমেদের ভাই না হলে কুত্তাও ফাক করতো না অথচ সুযোগ ছিল আপনার শুওড়ের খামারের মালিক হবার অথচ নিজেই শুকর হয়ে গু দিয়ে সারা শরীর মেখে ফেললেন নরপশু জাফর,1,celebrity
মাঘির পোয়া,1,celebrity
"জামাত-শিবিরের কুউউত্তার বাচ্চাদের মিছিল লেগে গেছে কমেন্ট সেকশনে!  তোরা বাঁশেরকেল্লায় গিয়া কাঠাতালপাতা খা, এইখানে কি শালারররপুতেরা?",1,celebrity
আরে কুত্তার বাচ্ছারা তোরা বিএনপি জামাতরা তো ক্রুসেডারদের থেকেও হিংস্র।রাজনৈতিক প্রতিদন্দী আওয়ামীলিগের বালও ছিরতে পারতিছিস না।সধারন মানুষের গা বোমা মারছিস। আর তোদের এই ঘৃন্য কর্মকান্ডের বৈধতা দান করছে এদেশের কিছু কুলাঙ্গার বুদ্ধিজীবি।,1,celebrity
শালারপুত দালাল।,1,celebrity
তুই মাদার***দ এখনো বেচে আছিস,1,celebrity
বদমাইশ তুই আছিস বলে বিনোদন নামক বস্তুটা এখনো ঠিকে আছে,1,celebrity
চুচিলদের টিয়ার মধ্যে গরম রডের চ্যাক দিতে হবে,1,celebrity
প্লিজ ষাঁড় আমাকে একটু চোদনা শিখান।  আমার বড়ই চোদনার অভাব,1,celebrity
"""জাফর"" নামটার থেকে কেমন যেন বেইমান বেইমান গন্ধ পাওয়া যায়..... সব জাফরই কী তাহলে মীর জাফর....?",1,celebrity
Condom তোর দোনের কাছে রাখ চোদনা,1,celebrity
"আপনি যে একটা ""ষাঁর"" তা এতো দিনে একটু হলেও অনুমান করতে পারলাম!!",1,celebrity
চোদনা স্যারের পোষ্টে কমেন্ট যারা করছে তারার কমেন্টে ৪-৫ হাজার লাইক।   অনলি স্যারের পোষ্টের কমেন্ট ইজ রিয়াল Älfâ Rãhmåñ Subel Nasim Shamim Omar Faruk Topu Iqbal Hussain Emu Shajinur Rahman Masum Ahmed,1,celebrity
প্রিয় ষাঁড়😂 আপনি কোন সেক্টরের মুরগি জবাই করেছিলেন? 😅,1,celebrity
দূর হালা জাঙ্গিয়া লীগ,1,celebrity
গরীব শালারপুত!,1,celebrity
লুইচ্ছা মাগির পোলা,1,celebrity
খাংকির পোলা মোনাজাত ধর,1,celebrity
"হালায় চুদির পোত,,",1,celebrity
তোর মত বিচিহীন মানুষ কে এই নিয়ে মন্তব্য করা অনুচিত হবে।।।,1,celebrity
শাউয়া...তোরে কেউ চোদে না শাউয়া...তুই এইবার অফ যা😡 তোর চোখের চশম জোড়া গোল গোল শাউয়া...তুই আস্ত একটা মাদারচো*🐸,1,celebrity
তুই একটা জাফর গরু 🐂 জাতের বাছুর।,1,celebrity
ভুতের বাচ্চা জাফর ইকবাল,1,celebrity
আহারে চশমার ফাক দিয়া যদি ষাঁড়ে নিচের কমেন্টগুলি পড়তো তাহলে নিশ্চিত একটা বালের ফিকশন তৈরি কইরা ফেলতো ।,1,celebrity
ফইরনির বাচ্চারা হাজির্।,1,celebrity
নাম্বার ওয়ান মাদারচোদ,1,celebrity
"আপনি চাটুকার। আপনি দলকানা। আপনি সুবিধাবাদী। আপনি গর্তবাসী। আপনি নকলবাজ। আর সর্বশেষ,পুরুষ হয়েও নারীর মত গর্ভবতী (যেহেতু আপনি বমি বমি ভাবে আক্রান্ত) 😃",1,celebrity
কুত্তে কা আওলাদ!,1,celebrity
তুই দালাল জাফর সেট,1,celebrity
কিরে জাফর তুইতো ব্যাটা  নাস্তিক তুই মারাগেলে মসজিদে শিন্নী দিবো,1,celebrity
ফইন্নির ঘরের ফইন্নির কথা হুনছো?,1,celebrity
"বলদ ইকবাল, কোদাল লাগবে? তোর লুকানোর সময় আসতেছে বদ...",1,celebrity
বাহ চুদির ভাই বাহ...নামাজ এর সময় বসে বসে পোস্ট করতেছেন?  কথা আছেনা- সময় সময়ের সাথে বয়ে যায়                       কিছু মানুষ আকাচোদাই রয়ে যাই,1,celebrity
শুয়োরের মুখে কথা ফুটেছে,1,celebrity
বাহ! চুদির ভাই বাহ!!!,1,celebrity
১০। চুতিয়ামুক্ত মিডিয়া এবং বুদ্ধিজীবি,1,celebrity
কুত্তাকে বাচ্চা,1,celebrity
হালা বলদ নং ওয়ান।,1,celebrity
চুদির ভাই। তুই বাইচ্চা আসত,1,celebrity
ছাগলের বাচ্চা তুই,1,celebrity
শয়তানের বাচ্চা জাফর ইকবাল,1,celebrity
গাধা অার ঘোড়ার যৌন মিলনে যে বাচ্চা হয় সেটাকে খচ্চর বলে।  অার পাকি এবং বাংলাদেশীর মিলনে যে বাংপাকির জন্ম হয় তাদের কে ছাগু বলে।   ছাগুদের হাটবাজার দেখতে অাসলাম কমেণ্ট বক্সে।  দেখি কোন ছাগু কত বড় করে ম্যাঁহ ম্যাঁহ করে ডাক দিতে পারে। 🙄🙄,1,celebrity
"শালারপুত এত বড় স্টেটাস পড়ার সময় নেই,, পরেরবার ছোট ছোট স্টেটাস দিস।",1,celebrity
অই শালার্পুত কেমন আসস?,1,celebrity
"আহা দালাল, আহারে দালাল আহা চাটুকার, আহারে চাটুকার আহা পা চাটা, আহারে পা চাটা।আহা গর্তবাসী, আহারে গর্ত বাসী",1,celebrity
"হালার বিচির সাথে ২ হালি ইট ঝুলিয়ে দিলে সব ঠিক হয়ে যেত,,,,,,,",1,celebrity
"নাপাকিস্তানের জারজ সন্তান, পাকি বীর্য থেকে জন্ম নেয়া অবৈধ ছাগুরা দল বেধে ফেইক আইডি নিয়ে ঝাপিড়ে পড়েছে।",1,celebrity
#দালাল #দালাল #দালাল,1,celebrity
"স্যার এখন মাগির দালাল, এম ডি,",1,celebrity
"ছি ছি কি লজ্জা তোমরা কি মানুষ তোমরা কি ছাত্র কিভাবে পার একজন শিক্ষিত, সুশীল, জ্ঞানী ও গুনী লোক কে এভাবে গালি ও নোংরা কথা বলতে   স্যার আপনি ওদের কথায় হতাশ বা লজ্জিত ও কষ্ট পাবেন না আমি জানি কারন আপনি একজন শিক্ষিত মাদারশুদ",1,celebrity
এই হালারে সকলে  এক এক্টা জুতা মার হালার দুনুগালে,1,celebrity
নাটক চোদাবি না।,1,celebrity
"এই যে সুদি__ভাই,যখন তোমার বদরুল লীগে ধর্ষন করে তখন তোমার এইসব চেতনার বস্তা গুলা কৈ রাখ? ঐ গর্ত তে???",1,celebrity
কুকুরের বাচ্চার চোখে ছানি পড়েছে।,1,celebrity
তোদের চাইতে বেশ্যা পল্লীর দালাল অনেক ভাল।,1,celebrity
এই হালার বাড়ির নাম পাল্টাইয়া নতুন নাম দিতে চাই 🐸 #গর্তবিলাস 🙃,1,celebrity
এস ডি সুমন আমি আগেই কইছিলাম মাদারচোদ স্যার মরে নাই ..তুই ত্যু না জেনেই জানাজা পরে নিলি ..,1,celebrity
আপনি শিক্ষক নামের একটা বুকাচুদা।,1,celebrity
"আচুদা লোক জাফরইকবাল,  গাঞ্জা খাইয়া পোস্ট চুদাস এক্সিডেন্টে তুই মরলে বেশি ভালো হয়তো :-/",1,celebrity
গাধা দেখতে এখন আর চিড়িয়াখানা যেতে হয় না।  শাহজালাল বিজ্ঞান ও প্রযুক্তি বিশ্ববিদ্যালয় গেলেই দেখা পরবে নামধারী মুসলিম। নামের আগে মুহাম্মাদ-কিন্ত কাজে কর্মে নাস্তিক।   এইসব কুত্তার বাচ্চাদের কারণে দেশ আজ বিপর্যয়ে।,1,celebrity
"চোদনা, তরে নিয়ে মানুষ আড়ালে না.. প্রকাশ্যে হাসাহাসি করে",1,celebrity
ছাগুদের কমেন্ট পড়তে আসলাম। খুব জ্বলা জ্বলছে ছাগুরা।,1,celebrity
"তুই রাজাকার,শুয়োরের বাচ্চা",1,celebrity
তুই কেন মরলিনা কুত্তার বাচ্চা তুই বেঁচে থাকলেতো ইসলামের ই ক্ষতি।,1,celebrity
তোরে পাইলে পুকদিয়ে বাঁশ বরি দি দাড়াই করাই রাখতাম,1,celebrity
"গু খা শালার পুত,গু খা 😡😡",1,celebrity
‌ তুই বেটা বিখ্যাত নাস্তিক,1,celebrity
"গাধার বাচ্চা জাফর ইকবাল,তুই তো একটা নরদামার কিট, ও নাচতিক",1,celebrity
"এইডা দেহি ছাগুর   খোয়াড়....?   ছাগু সমাজ এই খানে কাডল পাতা নেই,মগবাজারে লাইন ধরেন......",1,celebrity
তুই একটা হারামী মীরজাফর ইকাবাল,1,celebrity
"জঙ্গি শিবির এর চেয়ে এই কুত্তালীগ আরও ভয়ানক... এদেরকে নিষিদ্ধ করতে বলার মত বিচি আপনার নাই... সো , আপনার বিচলিততায় কারও আর কিছু যায় আসে না",1,celebrity
তুমি একটা পিওর মাদারচোদ।,1,celebrity
শয়তানের চেলা জাফর ইকবাল,1,celebrity
ছাগুদের কমেন্ট পড়তে আসলাম।,1,celebrity
"ওই মিয়া , #আন্দোলন শেষ , আন্দোলন নিয়া  তুমি পোস্ট দেওন #চোদাও কেন ? যাও মিয়া বই লিখে ,বেচো গিয়া :)",1,celebrity
"আপনি হলেন মাদার অব ভোট চুরনির দালালী কবুতর।  আপনি তুচ্ছ একজন সস্তা দালাল। ক্ষমা যেহেতু চাচ্ছেন, আপনাকে আমি ক্ষমা করলাম না।",1,celebrity
ছাগুদের কমেন্ট পড়তে আসলাম। :p (২),1,celebrity
তুমি যে কত বড মাপের দালাল বোঝা যায় ষ্যাড়😀😀,1,celebrity
"ধুর, ষ্যাউয়ার পুত। এগ্লা শেখ হাসিনা দেখলেও হাঁসবে। মাংগের ইতিহাস সুদাও মেয়া।",1,celebrity
কেউ থাকলে প্যাদানি দে জোরে,1,celebrity
কিরে বান্দির পুত তুই এখন কই থাকস,1,celebrity
মাদারচোদ,1,celebrity
হালারপুত নিজেই তো সৃজনশীল মারায়া আর সৃজনশীল প্রশ্নের এক্সপেরিমেন্টেশন কইরা আমাদের হোগায় আগুন দিসিলো। এখন ওরে ওকালতি করতে কে বলসে আবার? যে আমার বালের উপ্পদেষ্টা। একটা এফেক্টিভ সিস্টেম চালু করতে পারল না কোচিং লইয়া টানাটানি,1,celebrity
হালারপু বেচে আছে এখনো???,1,celebrity
Muhammed Zafar Iqbal জ তে জাফর ইকবাল তুই রাজাকার তুই রাজাকার ।,1,celebrity
", জাফর সার অবশ্যই জ্ঞানী মানুষ, বাট এক কুখ্যাত শয়তান ও প্রতারক। আমি চাই উনি দীর্ঘদিন বেচে থকুক। ওনার লেখাগুলি যুক্তিসঙ্গত। আওয়ামীলীগ চিরদিন থাকবে না। একদিন নামতে হবে, সেদিন থেকে প্রমাণিত হবে, আওয়ামীলীগের মন্ত্রী এমপিরাই প্রকৃত রাজাকার। তখন বিটিভি থাকবে না। তখন সব প্রমাণিত হবে কারা রাজাকার।  ভারতের দালালদের জালিয়ে দেওয়া হবে। সারকে একটা প্রশ্ন, ""নতুন ট্রাইব্যুনাল গঠনে বিদেশী পর্যবেক্ষকদের কেন ফেরত পাঠানো হয়েছিল? শাহাবাগে কেন টাকা দিয়ে ও জোরপূর্বক আদম ভাড়া করে আনা হত? (আমি সব জানি)।  বিএনপি জামাত রাজাকার নয়, রাজাকার আওয়ামীলীগ।  সার, রাজাকার প্রসঙ্গে সার স্নায়ুযুদ্ধকালীন পরাশক্তিদের ভুমিকার ইতিহাস জানে, গ্লোবালাইজেশন বুঝে, কালেক্টিভ সিকিউরিটি সিস্টেম বুঝে,  ডিপ্লোমেসি বুঝে, ফরেন পলিসি বুঝে, অর্থনীতি বুঝে, বিশ্বরাজনীতি বুঝে, জাতীয়তাবাদ বুঝে, বিশ্বসন্ত্রাস কে চিনে, সেকুলারিজম বুঝে, উদারগণতন্ত্র বুঝে, জাতীয়তাবাদের ধারা গুলি বুঝে, পুজিবাদের রাস্তা চিবে, ছোট ছোট উপপথ চিনে, রিজিনালিজম বুঝে, বিশ্বমোড়লকে চিনে, বিশ্বরাজনীতির বহু ইতিহাস ও মেরুকরণের কথা জানে, মুক্তিযুদ্ধের মৌলিক কাহিনী জানে, কারণ সে একজন খাটি দালাল, বাট জানেনা ১৬ কোটি বাঙ্গালী। তোদের ঘাড়ে আবারো মই চড়বে, অপেক্ষার প্রহর গণনা কর। ৪০০ বছরে তোরা মাইর খেয়ে কিছুই শিখিস নি। আবারও সেখানেই গেলি। আজ বিশ্ববিদ্যালয়ের ছেলেগুলি ও শিক্ষকমহল সব শারীরিক ও মানুষিকভাবে প্রতিবন্ধী। খুব লজ্জা বোধ হয়।",1,celebrity
"আ*দা গর্তযোদ্ধার মুখে এইসব ম্যা ম্যা ডাক আর কেউ শুনতে চায় না,বমি আসতেছে তোর লেখা দেখে। 😒",1,celebrity
"১৯৭৫ এ আপনার বয়স খুবই কম, মাত্র অনার্সে পড়েন। 😜  ১৯৭১ এ আপনার বয়স ছিল আরো কম, ডায়্যাপার পরতেন। 😜  এজন্যই মুক্তিযুদ্ধ করেননি। গর্তে থেকে সব দেখে এখন আমাদের গপ্প শোনান☺",1,celebrity
ওরে পাঁডার পো বলদ...এসব এখন আর প্রজন্ম খায় নাহ।,1,celebrity
তুই মাদারচোদ যুদ্দের সময় পাকিস্তানি হানাদার বাহিনীকে মানুষের মুরগী  চুরি করে খাওয়াইছিস আর এখন মুক্তিযুদ্ধের চেতনা চুদাস তুই বড় রাজাকার তোর ফাসি হওয়া দরকার।,1,celebrity
ছাগলটা কি এই সকল কমেন্ট পড়ে?,1,celebrity
গাঁজা খোর।  মাইয়া বাজ।  নাস্তিকের বাচ্ছা,1,celebrity
এই সাউয়া তো জুতার বারি খাওয়ার যোগ্যতাও হারাইলো,1,celebrity
"বেওয়ারিশ কুত্তারা আবার কমেন্টে এটাক করে..:p করতে থাক,তোদের জন্মপরিচয় চেনার জন্যে সেটা দরকার..!!",1,celebrity
চুদানির পো গর্ত  থেকে বের হইছে আবার😀,1,celebrity
", কমেন্ট বক্সের কমেন্ট গুলি দেখে চোখ সরিয়ে নিলেই কমেন্ট গুলি অদৃশ্য হয়না। থেকে যায়, তাই সাহস সঞ্চয় করে কমেন্ট গুলি পড়ে নিজের উপর হড়হড় করে বমি করেন।",1,celebrity
"স্যার, ছাত্রসমাজ আপনাকে চুদেনা।  তারিখ: ০৮.০৪.২০১৮",1,celebrity
মাদার চো‌দের বাচ্চা তোর মার ভোদার  নিবাচন হই‌ছে !,1,celebrity
"জানতাম আপনি মারা গেসেন, তাই গায়েবী জানাযা দিয়ে সওয়াব কামাইলাম। কিন্তু ভাগ্যের কি নির্মম পরিহাস আপনি জীবিত হয়ে আমাকে সওয়াব থেকে বন্চিত করছেন ভালো কথা,  যদি আমার  গুনাহ হয় তাইলে সিলেটে গিয়া হাত পা বেধে লেংটা করে ট্রাকের পিছে ঝুলায়া শাহবাগ এনে ফালাবো। দুনিয়াতে  না পারলে হাশরের ময়দানে, তবুও আপনার মতো বাইনচোদকে ছাড়  দিবো না...",1,celebrity
" KBমানবতা & শান্তির ধর্ম ইসলামের চির শত্রূ,কুলাংগার,­ লেবাসধারী ভন্ড-অভিশপ্ত,হি­ংস্র হায়েনার জাত, রাজাকার শুয়োরের বাচ্চাদের জন সমর্থন এখন শুন্যের কোঠায়!সেটা জেনেই দেশে অস্থিতিশীল পরিস্থিতি স্রিষ্টির জন্য সর্বাত্বক নাশকতার কুপরিকল্পনা করছে যে কোন কুফরী পন্থায়।এদের দেখা মাত্রই থুথু লাথি ঘ্রিনা সহ যেভাবে সম্ভব প্রতিরোধ & চিরতরে বাংলাদেশ থেকে পাকিস্থানে বিতাড়িত করা প্রত্যেক মুসলমান তথা বাংগালীর কর্তব্য।এদেশে থাকার কোন নৈতিক অধিকার নেই এই খুনি নরপশু,ধর্ম ব্যাবসায়ী,মিথ্­যাবাদী মুনাফেক হারামজাদাদের.…থ­ু…থু…থু।তোদের মুখে প্রস্রাব একবার…শতবার…হাজ­ারবার…লক্ষ কোটিবার",1,celebrity
"রাজাকারের বাচ্চারা আবার ম্যাঁ ম্যাঁ শুরু করে দিয়েছে। কে যুদ্ধ করেছে আর করেনি সেই হিসাব না করে তোদের বাপ রাজাকার,  আল বদর, আল শামসরা কেন দেশের সাথে বেঈমানী করেছে, পাকিস্তানীদের সাথে মিলে গণহত্যা করেছে সেই হিসাব কর শূয়র ছানারা।",1,celebrity
"বাপদের নিয়ে বই লিখসে, অবৈধ সন্তান আর বীজগুলো সুরসুর করে চলে এসেছে কমেন্টে জ্বলুনি মিটাতে। ছাগুবহুল এক অসুস্থ প্রজন্ম তৈরী হচ্ছে। প্যাথেটিক।",1,celebrity
"কনডম ফেটে যাদের জন্ম হয়েছে সেসব কোটার বলদগুলোই এখানে স্যারকে গালি দিচ্ছে। এদের মা ৭১ সালে পাকিস্তান ক্যাম্পে ভাত রান্না করতো, বাকিটা বুঝে নেন স্যার 😂",1,celebrity
একটা মানুস এতটা লির্লজ্জ কি করে হয়!!!এই লোক নাকি আবার একজন শিক্ষক। সে তার ছাত্রদের কি শিখাবে? জাফরের মত লোকেরা জানে নিজের স্বার্থের জন্য কি করে নিজেকে উলংগ করতে হয়।,1,celebrity
"আরে বোকচোদ, চাষার ছেলে মেধাবী হলেও তারা চাষা হবে আর ভুয়া মুক্তিযোদ্ধার সন্তানরা সভ্য হবে এদেশে। তোদের মত পা চাটা গোলাম থাকতে এদেশে মেধা তৈরি হবে না। আগে মানুষ হ পরে গ্যান চোদাস",1,celebrity
হালার মিরজাফর এর বাচ্চা গুলো একটা চাঁদ মুখ খানা দেখাতে আইছে।,1,celebrity
খান্কির পুলা,1,celebrity
হালারপুত কইত্তে আইলি তুই।মাগী চোদা শেষ হইছে বুঝি >_<,1,celebrity
"বুইড়া মাগি জাফর, ট্রেঞ্চ থেকে বেরিয়ে এসে কমেন্টের রিপ্লাই দে।",1,celebrity
"ছাগলের বাচ্চা এতদিন কই ছিলি রে, তোদের জন্ম কি পাকিরা দিছে যার পরে খোজ নেইনি, তাই এসব করছ।",1,celebrity
নামাজের দাওয়াত দিলে হেই পোলাডা জংগি হইয়া গ্যালো....??..খানকিরপোলা জুতাইদ্দা বাইড়ান দরকার তরে...তর মায়রে চুদি...গালিডা দিলাম না...মুখ খারাপ না করার নিষেধ আছে,1,celebrity
তেলবাজ নাস্তিক শুয়ার মাগিবাজ জাফ্রাকবাল,1,celebrity
আমি মাদারি দেখেনি তবে আপনাকে দেখার সুযোগ পেয়েছি,1,celebrity
ছাগলের বাচ্চা ছগলের পেট থেকে বের হয়েছে । 😄😄😄😄,1,celebrity
"শ্লা বোকাসোদা 😈 দুজন মরে নাই,ঘটনাস্থলেই তিনজন ম্রা গেসে। পরে পাঁচজন",1,celebrity
কুক,1,celebrity
জাফর এক বাল👌,1,celebrity
"এইতো মৃত্যুর পরও বিশাল বড় বালটা ফেলে দিলেন অবশেষে !   এখন টিসু দিয়ে মুছে শুয়ে পড়ুন কবরে , জাহান্নাম নিশ্চিত আপনার স্যার !",1,celebrity
তুমি বান্দির পুয়া,1,celebrity
"তুই একটা বাস্টার্ড,  নাস্তিক,",1,celebrity
বাহ্ চুদির ভাই বাহ্ 👏👌,1,celebrity
ওরে বানচোদ তোর এসব কথা পাবলিক আর খাই না। তুই যে হাসিনার দালাল সেটা সবাই জানে,1,celebrity
"বেশ্যার দালাল...যখন তোর আম্মা নিরপরাধ আন্দোলনকারীদের রাজাকার ডাকলো, তখন কই ছিলি?  তোর নানাই তো রাজাকার। তোর রক্তে রাজাকার আর দালালি থাকবো, এইটাই স্বাভাবিক ।",1,celebrity
"চুদির ভাই বলে আপনাকে বড় করবো না, ৭৩ এ হেলিকপ্টারের করে ব্যালট ছিনতাই হয়েছে শুনেছি বাপ দাদার কাছে, তোমরা আজকের পেপার কাটিং গুলারে ইতিহাস বনাবে অদুর ভবিষ্যতে তখন আমি আমার এই স্ট্যাটাস ইতিহাস হিসাবে দেখাবো। #চুদিরভাই",1,celebrity
তুমও #চুদিরভাই মুচের ফাক গলায়া সব মানুষ কার পক্ষে গেছে এটা কইলে আজকাল বাচ্চারা ও কান খাড়া করার বদলে অন্য জিনিস খাড়া কইরা ফেলে........,1,celebrity
শয়তানের বাচ্চা জাফর ইকবাল।,1,celebrity
জারজ স্যর আমি আসি কমেন্ট পরতে জানতে ইচ্ছে করে বমি কি স্যর।,1,celebrity
You big mad,1,celebrity
"আবালের হাম্বা ডাক আর কেউ শুনবে না পড়বেও না ,,কাজের সময় একটা কথাও বলে নাই এই (খাচ্চর লুচ্চাফর)",1,celebrity
হ্লা রাবিস,1,celebrity
#খবিশ  এতো দিন পরে ঘুম ভাংলো,1,celebrity
বেটা শয়তান পন্থ্যি মৌলবাদি।😜 সাম্প্রদায়িক পন্ডিত। কুত্তার সাথে নারীদের বিবাহ মানতে পারে। তবে নারির সাথে বোরকা মেনে নিতে পারে না। আমার কাছে তর তিন পয়সার দাম নাই।,1,celebrity
শুয়োর দের গর্তে থাকা টাই শ্রেয়,1,celebrity
"ওহে মুর্খচোদারা, তোরা জাফর ইকবালের একটা নখের সমানও হইতে পারবিনা। কারণ তোদের মাঝে মুক্তিযুদ্ধের চেতনা নেই",1,celebrity
"বাইনচোদ, মীর জাফর প্রতিদিন ছাত্রলীগ আওয়ামী লীগের কুর্তারা ধর্ষণ করে তোমার চোখে পড়ে না।",1,celebrity
নাস্তিক কুকুর,1,celebrity
তুই চোর তুই কাপুরুষ,1,celebrity
"এই দুচির ভাই খালি পোস্ট দেয়,, পোস্টের কমেন্ট পড়ে না।। পোস্ট দিয়ে ভালো দালাল সাজে।। চালু মাল।।🤓🤓",1,celebrity
ঠিক বলেছেন ষ্যাড়😁,1,celebrity
টানা তিন চার শুধু মুলা দিয়া ভাত খাইয়া আপনার মুখের সামনে কয়েকটা পাদ দিতে মন চাচ্ছে প্রিয় ঝাঁপড় শ্যার।,1,celebrity
খোবিস,1,celebrity
"অথচ টিপাইমুখ , ফারাক্কা , তিস্তা , করিডোর , রামপাল বিদ্যুত কেন্দ্র , সীমান্তে হত্যা , বানিজ্য ঘাটতি , ভারতের সব ৩ নাম্বার পচা মাল এদেশে চালিয়ে দেয়া --- কোথাও এই দেশপ্রেমিকদের টু শব্দ পাওয়া যায় না। সব এখন গর্তে , হাইবার নেশনে থাকা গরু , কোষ্ঠকাঠিন্য আক্রান্ত রোগি !অথচ দিনের পর দিন , মাসের পর মাস , বছরের পর বছর - এসব দেশপ্রেমিকরা অনলাইনে - অফলাইনে কত অসংখ্য মানুষের দেশপ্রেমিকত্তের পরীক্ষা নেয় , পরীক্ষায় পাশ ফেলের ফলাফল ঘোষণা করে।",1,celebrity
খানকির পোলা তুই তো নিজেই রাজাকার এর বাচ্চা,1,celebrity
কুত্তার বাচ্ছা তুই শিক্ষক জাতির কলংক তোর বিবেক বিসর্জন দিয়ে স্বৈরাচারের দালালীতে লিপ্ত হলি। . মৃত্যুর পর মানুষ তোকে জাতীয় বেইমান হিসাবে তোর নামে থুতু দিবে।,1,celebrity
এই মাদারিকে স্যার বলতে গেন্না লাগে ওয়াক বমি করবো😷,1,celebrity
ছাএরা মনে হয় এবার খবিশদের চিনতে পেরেছে ... Mr you are a number one stupid bcs your two eyes 👀 are blind!!!!!!!! You never seen that kind of protest in Bangladesh 🇧🇩 it’s not watching only Bangladesh it’s already known across the world 🌎 but still you are lying .,1,celebrity
"জাতীয় নির্লজ্জ বেহায়টা কি একদিনও পোষ্টের কমেন্টগুলো পড়েনা!চামচামি,দলালি,তেলবাজির লাগি ষাড়রে নোবেল দেয়া হোক।",1,celebrity
তোর হালা বলদ।,1,celebrity
নাস্তিকতায় মন্ত্রী হিসেবে জাফড় ষাড়কে চাই......,1,celebrity
হ্লারে ফাডা দিয়া ছুত।।,1,celebrity
"ষাড় মিরজাফর কষ্ট হয় আপনার জন্য, আচ্ছা আপনি কি এই পোস্ট বা চেতনা খাড়া করে আপনার দেয়া পোস্টের কমেন্ট পড়েন",1,celebrity
শুয়রের বাচ্চা জাফর সার আপনি ধর্ষকদের উৎসাহ দান কারী আপনি নিকেই বড় ধর্ষক। নির্লজ্জ বেহায়া তুই,1,celebrity
😂😂😂 কুকুর 😡😡😡,1,celebrity
#দালাল #দলকানা #যাফ্রিকবাল,1,celebrity
হালায় কি বাচ্চাকালে গরুর মুত খাইছিলো নাকি? এতো বেহায়া কেন,1,celebrity
#তুই_রাজাকার।☺,1,celebrity
কিরে বেটা শুয়ার পোষ্ট হিডেন/ডিলিট করলি কা?,1,celebrity
কমেন্ট সেকশন দেখলেই বুঝা যার রাজাকারের বিবি বাচ্চাদের পুটুতে আগুন লাগায়ে দিয়েছেন। তবে এদের বেশিরভাগ পাকিবীর্য থেকে জন্ম নেওয়া নিকৃষ্ট কীট ছাড়া আর কিছু না।,1,celebrity
"খানকির পোলা কোত্থেকে বাহির হইছত,,গুটিকয়েক পরগাছা ছাড়া তোরে আর কারো ছো...র টাইম আছে নি।।বা.....দ।।ওয়াক থু",1,celebrity
ষাঁড় মীর জাফর ইকবাল স্ট্রাইক,1,celebrity
"এই শাউয়ার চ্যাট, তুই কই?",1,celebrity
"বালের পোষ্ট,মুক্তিযুদ্ধের কথা নাই..",1,celebrity
জাফর ইকবাল  একটা মাদারচোদ,1,celebrity
"""আমি দুর্বল প্রকৃতির মানুষ। ""    এতটাই দূর্বল যে ছাত্রলীগের হাত থেকে নিজের বউকে রক্ষা করতে পারলেন না, আপনি যে বউ এর স্বামী হবার স্বামর্থ রাখেন না তা ছাত্রলীগ জানলো কামনে !!!!! জাতি জানতে চায় ।",1,celebrity
ছাগল দেখতে হলে এখন আর মাঠেঘাটে যেতে হয়না।।। জাফর ইকবালের পোস্টের কমেন্টেই ছাগল এর অভাব থাকেনা।।।,1,celebrity
মাগির পুত ভাট্টিচোদা,1,celebrity
আপ্নি একজন 'ভার্সিটির অধ্যাপক' তাই নিজের ওয়েট বজায় রাখুন।এসব ছাগলামী করলে শুধু শুধু  সম্মান হারাবেন!  নাকি 'কমেডি' লেখছেন...?,1,celebrity
খোবিস,1,celebrity
"আপনার বয়স হয়েছে;এসব ""বালছাল"" লেখা তো অনেক লিখলেন। এবারর অবসরে যান । আপনার লেখায় বিনোদিত হতে হতে পুরো তরুণ/যুবক জাতিই এখন হড়হড় করে বমি করছে...বিনোদন দিয়ে হড়হড়বতী বানায়েন না",1,celebrity
তুই একটা মীর জাফর,1,celebrity
"প্রিয় ষাড়,  মন খারাপ হলেই চলে আসি আপনার পোস্টের মন্তব্যগুলো পড়তে,  মন ভালো হয়ে যায়😝😝",1,celebrity
কুত্তার বাচ্চায়দি বাইচা রইছেরে,1,celebrity
নাস্তিক কুকুর ।,1,celebrity
"পাকি শুয়োরদের কমেন্ট পড়তে চইলা আইলাম , তাদের জাতীয় পশু আবার ছাগল :D",1,celebrity
"আবালীয় ইকবাল , এতদিন তোর সুশীলতা কই ছিলোরে চুতিয়া ?   আচ্ছা কও দেখি , কোন কোন ক্ষেত্রে তোমার চেতনার দন্ড খারায় আর কোন ক্ষেত্রে নেতিয়ে থাকে ? এই বিষয়টা লিখে জাতিকে ক্লিয়ার করো , নইলে জাতি বারবার তোমার অপেক্ষায় থাকবে ৷",1,celebrity
"তুই দালাল ,তুই দালাল।  গর্ত থেকে কেমনে সম্ভব জামায়াতের কাজকর্ম দেখার?? মিথ্যা আর কত বলবেন দালাল সাহেব??",1,celebrity
আপনাদের চাটাচাটি আর দালালীর কারনেই এই ধর্ষন - আর এর জন্য আপনিও সমানভাবে দায়ী,1,celebrity
তুই হইলি একটা উচ্চ পর্যায়ের মাদার চুদ।তুদের মতো দালালরা এই বাংলায় যতদিন থাকবে নতুন কোন মীরজাফরের প্রয়োজন হবেনা।,1,celebrity
তুই একটা জানুয়ার,1,celebrity
হালার পো একটা পাগল,1,celebrity
২য় মীর জাফরের মুখে মুতে দে...,1,celebrity
মাদারচোদের মুখে হিসু করতে মন চায়।,1,celebrity
শালার ফালতু কথা নিয়ে এখানে আইলি,1,celebrity
"আপনি সরলতার ভং ধরা একটা ইবলিশ। পিশাচের দোসর। হাতুরি পেটা হওয়া ছাত্র সমাজ আজ অবরুদ্ধ আর আপনি বিশ্বকাপ চুদাইতে আসছেন। চোখ বন্ধ করে আপনার মুখে এক দলা থুথু  দিলাম, ওয়াক থুঃ",1,celebrity
জিগাতলায় অন্য পক্ষ তোর মরা বাপ ছিলো শুয়ার্।,1,celebrity
কার কার পেটে জারজ বাচ্চা আছে যে বমি করতে ইচ্ছা করে?,1,celebrity
তুহ!বকচদ🐸🐸,1,celebrity
জাফর তুই একটা প্রথম শ্রেণির বেয়াদব,1,celebrity
"হালা বাইনচুত,,, সরি খারাপ কথা ব্যবহার করার জন্য।",1,celebrity
মাগীর পোলা আগে জানলে ভার্সিটি লাইফে তোর অটোগ্রাফ নিতাম না।,1,celebrity
"আপনি জাস্ট বালের একটা দালাল, আর কিছুনা।",1,celebrity
"আপনি চুতিয়া ( দু ভাষী), বাতাস বুজিয় নৌকার পাল তুলেন।হিহিহি",1,celebrity
নেংটি ইদুরের বাচ্ছা,1,celebrity
"কুত্তার বাচ্ছা জাফর ইকবাল নামের প্রচ্ছেদে একটা বই লিখব লিখব করে লিখা হচ্ছে না..  না আর কালক্ষেপণ  না, এইবার লিখতে বসেই যাব।।",1,celebrity
একে স্যার বলে কে?প্রশ্ন যখন আউট হয় তখন জাফর কি করে??আবার অনশন চোদাইছে নাস্তিকের বাচ্চা . . .,1,celebrity
কুকুরদের অতিরিক্ত কৌতূহল থাকতে নেই। মনিব যা করতে বলবেন তাতেই ভেউ ভেউ করা লক্ষী কুকুরের ধর্ম।  http://fakenews24bd.com/2018/04/13/%E0%A6%86%E0%A6%AE%E0%A6%B0%E0%A6%BE-%E0%A6%95%E0%A6%BF-%E0%A6%8F%E0%A6%AE%E0%A6%A8-%E0%A6%AA%E0%A7%8D%E0%A6%B0%E0%A6%A7%E0%A6%BE%E0%A6%A8/,1,celebrity
এখন কি চুদাইতাম,1,celebrity
দয়া করে কেউ অশ্লীল ভাষা চোদাবেন না।,1,celebrity
"চুদির পুত, এহন তোর বমি আসেনা? নাকি বমি আসলেও সেগুলা আবার গিলে খাস...",1,celebrity
চাকর ইকবাল(চাটেশ্বর)😑,1,celebrity
দ্রোণাচার্য ট্রেঞ্চোদবাল।,1,celebrity
"শুয়োরের বাচ্চারা দেশটাকে ইরাক আফগানিস্থানের মত বানাইতে চাইতেছে, জনগণের ক্ষমতা আগে জনগণকে ফিরিয়ে দে হালার পো হালা।",1,celebrity
জ তে জাফর তুই চুতিয়া তুই চুতিয়া....,1,celebrity
হালারপো দালাল কুত্তার বাচ্চা,1,celebrity
"মাগির পুত খবিশ,,,,মিরর্জাপর",1,celebrity
"জাফর ইকবাল শতভাগ ভুয়া,হাজার ভাগ মিথ্যাবাদী, লক্ষ ভাগ ভন্ড, কোটি ভাগ স্বৈরাচারের দালাল । যা উল্লেখ করলাম তার প্রতিটি গুণ তার এই লেখায় আছে।",1,celebrity
কুকুরের জীবনী পড়ে যে টুকু সময় ব্যায় হলো আমার জীবনে মনে হয় এই প্রথম  ডাস্টবিনে মুল্যবান   সময়টা ফেলে দিলাম ।,1,celebrity
"""মীরজাফর"" এর আদর্শকে কলঙ্কিত করেছে তারই শিষ্য ""অনলি জাফর""",1,celebrity
ছাগুদের কমেন্টে ছয়লাব।।।😂 😂 😂 😂,1,celebrity
এই হালার পুতের কি লজ্জা শরম কিচ্ছু নাই! কেমনে এত কথা শুনার পরেও বারবার দালালি করে?!,1,celebrity
কিছু খানকির পুলার জন্ম হইছে সব জায়গায় হা হা রিয়েক্ট দেওয়ার জন্য। এসব শুয়োরের বাচ্চারা তাদের মা বইনের ধর্ষণের পোস্টেও হা হা রিয়েক্ট দিবে।,1,celebrity
Sheikh Moinul Hassan...you r great   ছাগু পন্ডিত। তুমি মনে হয় ইন্ডিয়ান ছাগুদের উন্নত মানের বীর্জে উতপাদন হইয়া সকল বাংলাদেশের জনগনকেই পাকি বীর্জ ভাবিতেস।,1,celebrity
বুইড়া বয়সের বাচ্চা হওয়ার ভং ধরোনা শুয়োর 😡,1,celebrity
"জাফর ষার, তুই নিজেই তো সি.আই.এ এর এজেন্ট। লীগের চোদন খেয়ে জান বাচানোর চেস্টা করে লাভ নাই। আগা পাছা দুই দিক থেকেই মারা খাবি।",1,celebrity
কেউ স্যারকে অশ্লীল ভাষা চোদাইবেন নাহহ 😊,1,celebrity
#Sir #Chutiya,1,celebrity
বাথরুমে হাগ হাগতে এই শাউয়ার পোস্ট টা পরতে গিয়া আমার হাগা আটাকায় গেসে কেউ দমকল বাহিনী রে ফোন দেন,1,celebrity
"খানকির পোলা রাজাকার কি তো হোগার বিষ উঠানোর জন্য লেখেছে? মাতিয়া যে রাজাকার কিইছে হেইডার প্রতিবাদ করছে, সালার পুতে এই সাধারণ জিনিশ বুঝে না আইছে বুদ্ধিজীবী গিরি চোদাইতে।মাতিয়ারে কিছু কইলি না?",1,celebrity
জাফর হড়হড় বমি ইজবাল😱,1,celebrity
"ZAfar akta bal ar sir,.ahammok",1,celebrity
হ্লায় একটা গাঞ্জাখোর। গাঞ্জা খাইয়া লিখতে বসছিল... দালালের বাচ্চা দালাল,1,celebrity
এইডা কুওা,1,celebrity
"চুতমারানি, শাওয়ার লেখা লেখ???এত পড়তে গেলে, আন্দোলন এর ছবিগলো শেয়ার দেব কখন????",1,celebrity
"হায়রে বেশ্যাজীবী, তুই আর মেহেদি এম্পি আজ এক কাতারে চলে গেলি?? তোরাই আজ আবার শিক্ষার কথা বলিস? মে",1,celebrity
"প্রিয় ষাড়, কয়দিন আগে না আপনার মৃত্যুর গায়েবানা জানাযা হলো শুনলাম 😛😝😛",1,celebrity
"আরে গাধাঁর বাচ্চারা জাফর ইকবাল স্যার তোদের মতো ফেবু পন্ডিত বা ফেবু সুশীল না যে ওনি তোদের এইসব টাউটামি পড়বো।তারে যদি এতোই খারাপ লাগে তাহলে তার কাছে কেনন সবকিছু আশা করছ।দেশেতো বহুত বুদ্ধিজীবি,সুশীল,সেলেব্রিটি আছে তাদের কাছে যা চুতিয়ারা।",1,celebrity
বালের লেখায় হর হর করে হেগে দিতে ইচ্ছা করতেছে 😰,1,celebrity
নডির পোলা দুরে থাক😠,1,celebrity
"মদ খাইয়া ,মাগি চুইদা তর ঘুম এখন ভাংসে । তর মত জারজের দরকার নাই এদেশের , তুই তর ভাইয়ের মত মদ খা আর মাগি চুদ যাইয়া ব্যেশ্যা মাগির পুলা",1,celebrity
জাফর ইকবাল হচ্ছে একটা পাচাটা দালালের নাম। দেশবাসি এই দালালের ভুয়াচেতনার কথা এখন আর বিশ্বাস করেনা। সবাই এই পেইজকে আনলাইক করে একটা নিরব প্রতিবাদ করুন।,1,celebrity
বীচিহিন বলদ আর জ্যাফ্রিকবাল একে অন্যের পরিপূরক।,1,celebrity
দেশে ছাগলের আবাদ ভালই হচ্ছে দেখছি। কাঁঠাল পাতা চিবানো ছাগল ছানাদের কমেন্ট শুধু। ছাগলেরা পাল ধরে আসছে ল্যাদাইতে।,1,celebrity
আরে মাদারচোদের বাচ্চা যখন কোটা আন্দোলনকারীদেরকে রাজাকারের বাচ্চা বলল তখন কই ছিলি জানোয়ারের বাচ্চা?,1,celebrity
"বিকৃত মস্তিষ্ক, বিক্রিত মাল। ভণ্ড মীর জাফর ইকবাল।।",1,celebrity
বাইঞ্চদ তুই মরিস না ক্যান খানকির পুলা,1,celebrity
চুতিয়া জাফর।,1,celebrity
অসংখ্য পাকি বীর্য থেকে জন্ম নেয়া ছাগু ফেসবুকে জাফর স্যারের ফলোয়ার।,1,celebrity
জাতীয় গর্দভ।।।,1,celebrity
"এই বেশ্যা দালাল টা, মুক্তিযুদ্ধের মতো বিশাল সময়ে, দামড়া একটা বেডা থাকার পরেও, যুদ্ধে না যাইয়া, রাজাকার নানার আস্তানায় সময় কাটাইছে। এই বেশ্যা দালাল এখন মুক্তিযুদ্ধ বেইচা খায়।",1,celebrity
"স্যার আপনি একটা বুকাচুদা, লেখালেখি বাদ দেন,বমি আসে আপনার লেখা পডলে।",1,celebrity
"এখন কিছু খানকি মাঘির পুলা মাইয়া জাফর ষূয়োড় এর পক্ষে কমেন্ট করব বা করতেছে🐸। এরা টিক এইটা বলতে ছাইতেছে  ”জাফর স্যার আমাদের স্যার,উনি আমাদের অথবা আমাদের মা বোনদের রেপ করলেও সমস্যা নাই”🐸 আমার কমেন্টে সেইসব আছুদাদের নিজের ভার্জিনিটি/সতীত্ব হারাতে রিপ্লে দেওয়ার দাওয়াত করা যাইতেছে🐸",1,celebrity
"আম্নে আমেরিকায় বাল্ডাও ফালাইতে না পাইরা দেশি পন্ডিত সাজছেন, এখন অন্যজনের গণিতে সেরা হওয়ার ক্রেডিট নিতে  ধান্ধা শুরু করছেন, ফালতু কোনখানকার😜",1,celebrity
নাস্তিকের বাচ্চা জাফরুল্লাহ তোর স্বাধীনতা পক্ষে কয়টা ভোট  দিছত,1,celebrity
মাদারচোদ চামচামি বাদ দে।,1,celebrity
ভুতের বাচছা জাফর ইকবাল???,1,celebrity
ষার ১৯৭১ রে যদি আমি থাকতাম তাহকে তোরে পুটকি মেরে তার পর মুক্তিযোদ্ধে যেতাম!  কুত্তার বাচ্চা তোরে আর কি কমু দয়া করে কমেন্ট গুলা পড়! পড়লে তোর বউ মেয়ে দুই জনেই প্রেগনেন্ট হয়ে যাবে। কেও আসছ একটু গ্লিসালিন দে হালার পোলারে পুটকি মারি!!!,1,celebrity
ওরে মাগিরভাই বাইনচোদ আইছোছ আবার চেতনা দেখাইতে! দূরে গিয়া মর,1,celebrity
ভাড়া তুমি বেচেঁ আছো?  তাহলে পোলাপান গুলা কার গায়েবি জানাজা পড়ছে।😂😂😂,1,celebrity
বালের মুক্তিযুদ্ধের চেতনা। স্যারের মাথা আছে মগজ নাই।,1,celebrity
স্যার প্লিজ আপনি আর পোস্ট দিয়েন না।আপনি যে মাদারেচোদ সেটা আর আমাদের দেখাতে হবেনা,1,celebrity
গর্তযোদ্ধা। চামচা দালাল।,1,celebrity
. ছাগুকুল আসো তোমারা এখানে স্যার কাঠাল পাতা রেখেছে দলে দলে এসে কাঠাল পাতা খেয়ে যাও . বাংলাদেশে যমুনা পাড়ি আর ব্যাক ব্যাঙ্গল ছাড়া আর এক ধরনের ছাগল আছে এদের না দেখলে বুঝতাম ই না.. . .জারজ শিবির.. আর কুত্তার দল বিএনপি পতিতালয়ের কন্ডম দূর্যটনায় জন্ম নেওয়া বেজন্মা গুলো এখানে এসে বাজে কমেন্ট করে ওদের পতিতা মায়ের মুখ উজ্জল করে,1,celebrity
"ছাগুরা দেখবেন রাস্তা ঘাটে মা বোনদের কে গালি শোনাতে পছন্দ করে,এখানেও কিছু ছাগু পাবেন।",1,celebrity
"বালের পোস্ট এতো বড়ো পড়তে মন চায়না, তবে কমেন্ট পড়ে মজা পায়😜😜😜😜",1,celebrity
আপনার মতো নাস্তিক আর আম্লীগের পুটকি চাটা বুদ্ধিজীবীকে বিচিতে চাপ দিয়ে মেরে ফেলা উচিৎ।,1,celebrity
আবালের সরকার। আবাল শিক্ষামন্ত্রী। আবাল প্রধানমন্ত্রী।,1,celebrity
আপনার বাশ খাওয়া খুব শখ জাগছে তাইনা? চুপচাপ ছিলেন এটাইতো ভালো ছিল। এবার লন ঠেলা।,1,celebrity
আ........চোদা৷৷৷৷৷৷৷৷  হালায়....... ওরে যে কোন পাগলে teaching দিসে......? আল্লাহ জানে only,1,celebrity
আমি দুর্বল প্রকৃতির মানুষ'।  খালি জামায়াত-শিবিরের গোয়া মারার সময় তুমি সবল প্রকৃতির মানুষ হয়ে যাও। শালার বুইড়া খাচ্চোর! তোমারে ঘৃণা জানাইতেও ঘৃণা লাগছে।,1,celebrity
"চুদানি, বাংলা খাইয়া আবোল তাবোল লিখছে। কষ্টের বিষয় হলো, হালায় কমেন্টস গুলো পড়ব না। মুছ,  দাড়ি, ------পেকে গেলেও ওনার যে এখনো অনেক কিছু শিখার বাকি আছে কেডায় হেতারে বুঝাবো.....",1,celebrity
"বালের কথা চোদাইতে আসছে।কোন কথা নাই,হড় হড় করে বমি করে দে।",1,celebrity
মদ খা খানকির পোলা,1,celebrity
সালার পুত মদ খা.....  মদ খা।,1,celebrity
হালারপুত হালা তোর লেখা কেন যে পড়লাম..খাড়া আমি এখনই বমি করে আইতাছি,1,celebrity
এই শালার বাপ ছিল রাজাকার। এখন নিজে খুব চেতনাবাজ দেখায়।,1,celebrity
"টিনের চালে কাওয়া, তুমি আমার শাওয়া",1,celebrity
জাফর শুয়ার,1,celebrity
আপনি তো শিক্ষিত মূর্খ দালাল পা চাটা গোলাম!,1,celebrity
ওই খানকির পোলা। আর কত দালালি করে খাবি। শিবির কি তোর বৌয়ের পুটকি মারছে নাকি😬😬😬,1,celebrity
"বাংগালীকে কুলাঙ্গার বানাইয়া রেখেছেন আর এখন চাচ্ছেন অন্ধ্য বানাইতে?... আপনার লেখা ও আপনাকে দেখলে  পুরাই মীরে জাফরের বংশধরের মত লাগে। পালানোর রাস্তা পাবেন না,😡..বাংলাদেশের স্টুডেন্ট কুলাঙ্গার? 👿...  কি ভাবছেন?.",1,celebrity
মদ খাবা আর ষ্যাঁর চুদবা,1,celebrity
হায়রে জারজ ! তোরা আবার শিক্ষক?,1,celebrity
.... ঐ ইন্দুর তোই মরছ নাই?,1,celebrity
হালার পো হালা। তোরে গরু দিয়া চোদানো দরকার।,1,celebrity
জাফর হলো একটি মুসলিম নাম  আর তিনি হলেন এক জন মনে প্রানে নাস্তিক তাই তাহার নাম হওয়া উচিত  জারজ BAL মানে  জারজ বাংলাদেশ আওয়ামিলীগ,1,celebrity
ছুদিরভাই,1,celebrity
ছাগলের ঘরের ছাগল । আচ্ছা তুই কি পড়াস তোর ছাত্রদের? আর তুই ই বা কি জানিস? দেশের শিক্ষক যদি এমন হয় তবে এই জাতি কি করে মনীষী/কান্ডারী জন্ম দিবে ??,1,celebrity
"হালায় মরে নায়,তাইলে হালারে কিছু গাঁজা দে খাইয়া আবার ঘুমাক।",1,celebrity
ষ্যড় মীর জাফর আপনাকে অগ্রিম ঈদ মোবারক,1,celebrity
কুত্তার বাচ্চা,1,celebrity
- সালারপুতের এতোদিন পর ঘুম ভাংছে..! স্লা তোরে লাগবে না যা মদ খেয়ে ঘুমিয়ে পর 😒👿,1,celebrity
Zafar iqbal tor myre chudi,1,celebrity
"বাটপার ধোন বিজ্ঞানী আপনি নিজের উঠোনে ট্রেঞ্চ খুঁড়ে লুকিয়ে থেকে যেভাবে  মুক্তিযোদ্ধা  সেজে মুক্তিযুদ্ধের গল্প শোনান...ঠিক বাংলাদেশের নির্বাচন আপনার ট্রেঞ্চের গল্পের মতো হয়েছে....আপনাদের মতো শিক্ষিত অমানুষ গুলা নেক্সট জেনারেশন কে ধ্বংস করছে.... আপনি দালাল আপনি বাটপার,আপনি বুদ্ধি বেশ্যা",1,celebrity
তুই মাদারি এখনো বেচেঁ আছিস?  হালার পো,1,celebrity
আমেরেইকা কি চোদাইতে গেছিলি মাদার চোদ,1,celebrity
#শালারে গর্তে থাকতে হবে আবারও,1,celebrity
বাড়া তুমি মরে গিয়ে কিভাবে ফেবু চালাচ্ছো।তুমি বাড়া নিশ্চয় ভূত বাড়া।,1,celebrity
জাফরের অপর নাম লুচ্চা....,1,celebrity
তুই জাফরবাল একটা রাজাকার,1,celebrity
লুইচ্চা মাদার ফাকার তোর আসল রুপ পোলাপান বুঝতে শিখছে।,1,celebrity
"ছাগুদের ম্যা ম্যা আওয়াজে চারপাশ ভারী হয়ে উঠেছে।  রাস্তাঘাটে চোদা খেয়ে,ছাগুদের প্রিয় স্থান এখন মানুষের কমেন্টসবক্স",1,celebrity
জাফর স্যার আপনার নুনুর সাইজ কত?,1,celebrity
দূর লুচ্ছা,1,celebrity
বালের জাফর ইকবাল,1,celebrity
ছি ! ছি ! ছি! দালাল কোথাকার !!,1,celebrity
"খানকির পোলা চুতমারানীরা ১২১ কোটি টাকার যে ভাগ নিলি ফেসবুকে প্রচার করার জন্য,  শালারা কই তোরা !!  স্যারের পক্ষে কমেন্ট কর মাগীর পুতরা। চুতমারানী তুদের ২০০০ জনের নামেই আপার কাছে বিচার দিমু। টাকা খাস আবার কমেন্ট চুদাস না !",1,celebrity
তুইতো হলে নাস্তিক আওয়ামী লীগের  দালাল,1,celebrity
চেতনা বাবু চলে আসছে। চারদিকে প্রশ্ন ফাঁস কইরা বই লেখন চোদাউ? 👿,1,celebrity
স্লা গর্তে লুকাইয়া তুই আবার চেতনাগিরি দোচাস,1,celebrity
ছাগুদের কমেন্ট পড়তে আসলাম!,1,celebrity
কুটা ছাগলদের কমেন্ট দেখতে আইলাম। চক্ষে পানি আইসা পড়ছে!!!,1,celebrity
"যদি সেদিন রাতে তোর আব্বু কন্ডম ইউজ করতো তাহলে আজ এই পোস্ট দেখা লাগতো না আমাদের 🐸  বাই দ্যা রাস্তা,,,,, `kanker pola tor gorto koi`",1,celebrity
বাহৃ চুদির ভাই বাহ্।,1,celebrity
এই সব আজাইরাগোরে  বিমানের উপরে তুলে পুটকি মারা উচিত।। যেন পডে যাওয়ার ভয়ে পুটকি মারা দিতেই থাকে। #benchoo 😡,1,celebrity
"# স্যার, আপনার মোচের কারনে আপনারে কেমন জানি রাজাকার রাজাকার মনে হয় ৷ গোঁফটা ফেলে দিলে ৭১ সালের গর্ত খুড়ে থাকা তরুণ ভীরু মুক্তিযোদ্ধা দেখাবে ৷  # স্যার! এই বাংলাদেশে কোটি কোটি তরুণ আছে যাদের সামনে গিয়ে যদি বলেন: - আমি জাফর ইকবাল ""সঙ্গে সঙ্গে  তারা ঘৃণায় হর হর করে আপনার গোঁফের নিচে বমি করে দিবে ৷",1,celebrity
"ছাগুরা এসে গেছে ম্যাঁ ম্যাঁ করতে। ছাগুর বাচ্চারা বাঁশেরকেল্লায় যা, এখানে কাঁঠালপাতা নাই। স্যার কোন বিষয়ে কথা বলবেন না বলবেন এটা তাঁর একান্ত ব্যক্তিগত বিষয়। তাছাড়া,  উনি প্রতি দুই সপ্তাহে একটা কলাম লেখেন এবং তাঁর ছাত্ররা সেটা পোস্ট করেন বৃহস্পতিবার রাতে। সুতরাং, সঠিক সময়েই লেখা এসেছে। বাঁশেরকেল্লায় গিয়ে ম্যাঁ ম্যাঁ কর।",1,celebrity
"আল-কুরান & হাদিসের অপব্যাখ্যাকারি,ধর্ম ব্যব্সায়ী,যুদ্ধাপরাধী,খুনি-ধর্ষক,ভন্ড,রাজাকার,জংগী সংগঠন জামাত-শিবির(থু…থু…থু…) এর শুয়োরের বাচ্চারা আজ বিক্ষোভ মিছিলের ঘোষনা &বাধা দিলে লাগাতার ৭২ ঘন্টার হরতালের যে দম্ভোক্তি গত কাল দেখাল…পা চাটা দালাল,কুত্তার বাচ্চা হিংস্র সেই হায়েনারা আজ কোথায়.…?",1,celebrity
এই সব কমেন্ট যারা করে তারা মানুষের বাচ্চা না তারা জানোয়ারের বাচ্চা,1,celebrity
তুই তো একটা মির-জাফর শুয়ার😡😡,1,celebrity
"বান্দির পুত তুই যদি আমার এলাকার হইতি, তর মার শাউয়ার বিত্রে তরে ভরে দিতাম",1,celebrity
দূর হো বেটা বদমাইস মিরযাফর,1,celebrity
জামাত- বিএনপি কি তুমাকে হুগা মারে।,1,celebrity
"১৯ বছরের_টগবগে 'ছাগল', মুক্তিযুদ্ধ না কইরা চুল কাইটা ফাকিস্তানিদের নজর থেকে বাঁচতে চায় আবার মুক্তিযুদ্ধের চ্যাতনা ফেরী কইরা বেড়ায়. খা:মা:পো: __😤",1,celebrity
আ।।।।।।।বা।।।।।।।।ল।,1,celebrity
"সম্মান করতাম এখন সম্মান করতে মন চায়না, বাচ্চাদেরকে কেন্দ্র করে সমাজে ভাল মানুসের মুখোশ তৈরি করেছেন। এখন পিছনে ফেলে পুটকি মারা আলাপ চুদাইতে আইছে খাংকির পোলা😡😡😡",1,celebrity
"এক শ্রেণির চুতিয়া, মাদার*দ আছে এরা আজ ৩ দিন জাফর স্যারের কলাম নিয়ে খুব প্রশ্ন তুলেছে। শালারা এটাই জানে না যে স্যার কবে কবে কলাম লিখে। ওই সব ভন্ডদের মুখে থুথু মারি যারা জাফর স্যার কে বিতর্কিত করার চেষ্টা করেছে।",1,celebrity
"ছোট বেলায় ""জাফর ইকবাল সমগ্র"" বইটা টানা পড়ে শেষ করেছিলাম,  ভালবাসতাম আপনাকে।  ২০১৮ এসে আপনাকে খাবার না পাওয়া নেড়ি কুত্তার মত লাগে।",1,celebrity
তুই একটা মীরজাফর। জাতির শত্রু,1,celebrity
গাফর ১বাল তুমি আর কুত্তার হাগু এত মিল কেন??,1,celebrity
এই চেতনা বেশ্যাটার কি সামান্যতম হায়া শরমও নাই?!?!,1,celebrity
ধুর হালা চামচা..😂😂,1,celebrity
"মুতিয়া চুদির জি সংসদে যদি বলতে পারে আন্দলন রত সকল ছাত্র রাজাকারের বাচছা তখন, আমি রাজাকার বলতে সমস্যা কি?? আপনি মুতিয়া চুদির কথাটা কেনো আনলেননা। নাকি নাম নিলে, আপনি রাজাকার হয়ে যাবেন তাই",1,celebrity
জাফর ইকবাল এর মত দালাল রাই বর্তমান যুগের রাজাকার,1,celebrity
হালার পুত!!,1,celebrity
"ভুস্কির পোলা কই আছিলি এতদিন,  এখনতো তোকে হড় হড় করে চুদে দিচ্ছে।",1,celebrity
"শুয়োরের বাচ্চা, নুরু রাশেদের গগন বিদারি চিৎকার তোর কানে যায় না?",1,celebrity
"গরীবচোদা, বর্বর, ফকিন্নিরবাচ্চা, মদ খাবি মানুষ হবি। মদ না খাইলে তোর উপত্যকা চুদি।।",1,celebrity
"আচ্চা, আবালডা কি কমেন্টগুলো পড়ে নাহ...!!!",1,celebrity
"ছাগল গুলা কাঠাল পাতা মনে করে, খাওয়ার জন্য এসে ভিড় জমিয়েছে... ছাগুর বাচ্চারা তুরা অার কবে মামনুষ হবে.???",1,celebrity
শুয়োরের বাচ্চা একটা,1,celebrity
ফকিরনির বাচ্চারা তাদের বমিমার্কা কমেন্ট নিয়ে হাজির্। এদের নিজেদের বমি জোর করে খাইয়ে দেয়া উচিৎ !,1,celebrity
"ষাঁড় , কখনো যদি ভুল করে ও মসজিদে যান তাহলে কি নামাজ পড়া বাদ দিয়ে ইমাম সাহেবের ভুল ধরবেন ? জাতি জানতে চায় 😏😏",1,celebrity
খানকির ছেলে!!!,1,celebrity
"মানুষ বাইঞ্চোদ হয়, তারপর চুদিরভাই হয় এরপর আসে জাফর ইকবাল(বিশিষ্ট গর্তযোদ্ধা)",1,celebrity
জাফর ধান্দাবাজরে আমার কুওাও চোদবে না  খাংকির পুলা ব্যাশ্যা -সিফাত উল্লাহ সিফাতী,1,celebrity
অই মাদারিদের বিচিতে নু+নু বার করে লাত্তি দেওয়া উচিত বাড়া😒😒,1,celebrity
কুত্তার অহেতুক ঘেউ ঘেউ। যেনো খোলা পায়খানা থেকে আহার নিচ্ছে স্বগোত্রীয় হয়ে।,1,celebrity
জানোয়ার তুইতো দেশের সবচেয়ে বড় রাজাকার,1,celebrity
খান্কির পোলাটাকে দালালীর জন্য দ্রুত নবেল দেবার জন্য আহবান জানাচ্ছি,1,celebrity
"আহারে, শালার চ্যাটের বালটা বাঁচি আছে, চেতন হলো!",1,celebrity
"আহা নির্লজ্জতা! আপনি শিক্ষক নন আপনি ধর্ষক।শিক্ষা,সাহিত্য,সংস্কৃতি,চেতনা,বিশ্বাস,মূল্যবোধ ক্রমাগত গণধর্ষিত হচ্ছে আপনার দূর্গন্ধযুক্ত লেখায়।   চাটুকারিতার বদহজমে আক্রান্ত নির্লজ্জতাও বুঝি লজ্জায় হড় হড় করে বমি করে দিয়েছে।ছি!  ছি!",1,celebrity
ফকিন্নির পুতেরে একটা গালি দিতে ইচ্ছে করে!,1,celebrity
মদ খা শূয়র।,1,celebrity
"কিরে খানকির পোলা,,,",1,celebrity
আপনি যতক্ষণ ছাগুদের সমর্থন না দেবেন ততক্ষণ পর্যন্ত ছাগুরা গু ছাড়া কিছু মুখে নেবে না বলে মানত করসে,1,celebrity
"হালারপুত কুত্তার বাচ্চা, তুর গোফ গুলো টেনে ছিডে ফেলতে ইচ্ছে করে।।",1,celebrity
নাস্তিক কুত্তাগুলা এই রকমই হয়।,1,celebrity
হেডার হুত চার দিন পারে আইছে fb তে এতো দিন কৈই আছিলি মাদারটোস্ট,1,celebrity
এরে সতানের বাইচ্চা দালাল কতুন বার অইছত তুই?,1,celebrity
কমেন্ট বক্সে এত বাংপাকি বেজন্মা শিবির আহে কই থেকে?,1,celebrity
"আপনি তো পুঙ্গার পোলা কিছুই জানেন না। হলিউড মুভি নিযা বই লেখো আবার সাক্ষাতকার চোদাও। বিদেশিরা যদি বলে বসে আপনার বইগুলা তো রিমেক করা,তখন তো তোর গোয়া শুকাই যাবে। সেজন্যই আর কি,বুঝিনা মনে করছস হ্লা",1,celebrity
"আপনি যে একটা মাদারচোদ আকের বার প্রমাণ হলো,,তার কারন হলো দশ বছরে যে পরিমাণ গুম খুন হয়েছে সে গুলো কিছুটা তুলে দরা উচিত ছিলো,,আর মুক্তিযোদ্ধা কথাটি আপনার মতো আবালের কাছে মানায় না।আপনি একটা অসৎ লোক।",1,celebrity
বেটা মাদারটোস্ট,1,celebrity
"চোরাইকবাল, তোর লেখার মাঝে ই দালালীর গন্ধ। এতো মানুষের ঘৃণা নিয়ে বেচে আছিস কি করে?",1,celebrity
খা😡নকির পোলা এতোদিন কই ছিলি তুই? তোর চেতনাবোধ তোর পিছন দিয়েই ভরে দিবো। ভাইয়েরা আমার রাস্তায় মার খাচ্ছে আর উনি এতোদিন পর এসে নাটক চোদাচ্ছেন 😡,1,celebrity
পাকি শুয়ারের বাচ্চাগুলো পাগল হয়ে গেসে....কমেন্টসে চুল ছিড়তে আইসে...,1,celebrity
আপনি তুক্কো তুই যে এক দুই তিন চার দিয়ে এক এক করে প্রশ্ন করে যাচ্ছস তুরে খাওয়ার টাইম আছে নাকি বান্দির পুত??👹 👹,1,celebrity
"জাপর ইকবাল তোরে এবং মুরগী চোরা শাহরিয়া কবির রে কুত্তার মত পিডাইবো সময় আসতেছে মনে হনে রাখিছ! আমার দলকে ব্যবহার করে তোরা ইসলামের অনেক হ্মতি করেছস, এর জন্য প্রস্তুত হ।",1,celebrity
এই বোকাচোদারে কেও ফাক কার পিলিগ😖,1,celebrity
"........... এখন আর তোমার লেখা পড়ে বমিও আসতে চায় না। যেটা আসে সেটা রক্ত বমি। লেখার শুরুতেই তুমি লিখেছ ""ভারতবর্ষ""!!!!  কি আশ্চর্য!!!!  ভারতবর্ষ ভাগ হয়ে প্রথমে ২ টা পরে ৩ টা  স্বাধীন দেশ হলো, আর তুমি ভারতের কট্টর মালুদের মত ভারত আবার বাংলাদেশ 🇧🇩, পাকিস্তান দখল করে ভারতবর্ষে পরিনত হবার স্বপ্ন দেখো!!!!!! তোমার মত দালালেরা আসলেই যে দেশদ্রোহী সেটা কিছু বলদে এখনও বুঝে না। এখানে এই কমেন্টে ও সেই সব বলদ এসে ম্যা ম্যা করবে।",1,celebrity
"আপনি নবাব সিরাজউদ্দোলার আমলে থাকলে ব্রিটিশরা আপনার পুটকি মেরে গাঙ করে দিত,মীর জাফরকে পুটকি মারতে পারেনি তেলের অভাবে মাগার আপনারতো পোষ্টেই অনেক তেল।তেলে কমিয়ে মারেন,তা নাহলে কোন দিন বাঙ্গালিরাই আপনাকে পুটকি মেরে গাঙ করে দেবে",1,celebrity
ধরি মাছ না ছুই পানি' র আধুনিক ভার্সন 'হাগমু কিন্তু পাছা ভিজামু না' বা 'চাটমু তবে লালা ঝরাবো না'--- জাফর স্যার,1,celebrity
জাফর বোকাচোদা  👎👎👎 দালাল👎,1,celebrity
দালালী চুদানোর জায়গা পাইলি না,1,celebrity
আপনার এই সুশীল কথা কেউ চুদে না স‍্যার,1,celebrity
জাতীয় মির্র্জাফর,1,celebrity
জুতা মার শালারে,1,celebrity
বাইঞ্চু তুই তো বড় রাজাকার ছিলি। ১৯ বছরের যুক গর্তে লুকিয়ে কি রাজাকার দের মতো ধর্ষণ করতি,1,celebrity
সালারপুত এত বড় করে লেখা লিখস কেন?পড়তে পড়তে মাথা ঘুরে মাটিতে পড়ে যদি মরে যাই তার দায় বার কি তুই নিবি বাইনচুদ।,1,celebrity
"চাড়ালের বাচ্চা, জামাত যে আওয়ামীলীগ এর সাথে ছিল তা নিয়ে কিছু বললি না...?",1,celebrity
চোদানির পুত তোরে এত বড় গল্প লিখতে কে বলছে? অর্ধেকটা পড়েই মুখে অসংখ গালি চলে আসলো।,1,celebrity
ছাগুদের কমেন্ট পড়তে আসলাম। :p,1,celebrity
এরে স্যার বলে কিসের জন্য এরে বুদ্ধি বেশ্যা বলা উচিত।,1,celebrity
আমি ভুদাই দেখিনি কিন্তু জাফর ষাড়কে দেখেছি,1,celebrity
একটা যৌক্তিক আন্দোলনকে ভিন্ন খাতে নিয়ে বিফল করার যে চেষ্টা করলেন তাতে আপনি সারাজীবন সাধারণ ছাত্রদের কাছে চুদির্ভাই হিসেবেই থাকবেন.. ওয়াক থু,1,celebrity
"মাদার টোস্ট,ফেসবুকে বমি কইত্তে আইছ?",1,celebrity
"কিরে নটির ছাওয়াল,তোর কি মানুষ হইতে ইচ্ছা করে না?",1,celebrity
বদমায়েসের সুর কি!! 'অত্যন্ত মানবিক'। পা-চাটা কোথাকার।,1,celebrity
খানিকির পোলা!,1,celebrity
আরে ষাঁড় নাকি!  শোকে আর গর্তে থাকতে পারেন নাই নাকি? তালিয়া হবে আপনার জন্য 👐✋👐,1,celebrity
দূর বোকাচুদা এত বড় স্ট্যাটাস দিসেন কেন? এত বড় স্ট্যাটাস পড়ার সময় নাই আমার।,1,celebrity
ষাড়্ আপনার The ষোয়রের মত মোচ,1,celebrity
"এসব আবালচোদা ষাড়রা আওয়ামী লীগের মধ্যে যুদ্ধ অপরাধী  খুঁজে পান না, একচোখা আওয়ামী আর ভারতীয়  দালালের বিচার হবে যদি সময় হয়।",1,celebrity
শালার পুত তিনদিন পরে তোমার ঘুম ভাংছে। কয় কলকি খাইছিলা চুদিরভাই,1,celebrity
কুকুরের মুখে গরুর ডাক মানায় না!!!,1,celebrity
স্যার আমনের মেয়েরে চুতিয়া,1,celebrity
হালারপুত মদ খা মানুষ হ!,1,celebrity
আরে হারামজাদা! তুমি কত টাকা খাইছো???,1,celebrity
খা নকির পোলা ষাড়,1,celebrity
হালা সরকারের দালাল!!!  কোটা নিয়ে সাধারন শিক্ষার্থীর আন্দোলন তোর চোখে পড়ে না??এসব নিয়ে তো তোরে কিচ্ছু লিখতে দেখি নাই।,1,celebrity
খানকিরপোলা💜💘,1,celebrity
"আমাদের সিলেটের পাক মাটিতে তুমার মতো নাপাকেরে জায়গা দিছে কেডা,",1,celebrity
....এই লোকটাকে পাছায় লাথি মারে বের করে দিয়া উচিত বেটা দালাল...Ahmed Redwan Haque,1,celebrity
তোর সাউআ,1,celebrity
তুই নাস্তিক,1,celebrity
খবিস হয়ে গেছেন স্যার। বাচ্চা পোলাপান এর বমি দিয়ে গোসল কইরা আসেন স্যার।,1,celebrity
ফকিন্নির পুত জাফুইরগা,1,celebrity
নাস্তিকগুলি এমন ছাগু মার্কাই হয়?,1,celebrity
"পাকিস্তান আমলেও অনেক বেশি ধর্ষণ হতো, স্যার জাফর ইকবাল ও ধর্ষণের ফসল।",1,celebrity
মাদার চোদের বাচ্চা,1,celebrity
আমি রাজাকার তবু তোমার মতো দালাল না,1,celebrity
এই ছাগু গুলার কমেন্ট পরে আচ্ছামতো গালাগাল করতে মনে হয়। আবার মনে হয় কি হবে? গাধা পিটিয়ে তো আর মানুষ করা যায় না। যেমন যায় না বেশ্যাকে মিষ্টভাষী করা।,1,celebrity
কমপ্লিট চুতিয়া।,1,celebrity
জাতীয় বোকাচোদা,1,celebrity
আপনাকে আর দোচার টাইম নাই। আপনাকে স্যালুট। 🖕🖕🖕,1,celebrity
বোকাচুদা জাফর!,1,celebrity
"অই খানকির পোলা ফারাবী,পত্রিকার তারিখ টা খেয়াল করছোস,আর তোর এগুলির কি বালের সত্যতা আছে,তোর মা পাকসেনাদের সাথে বেড শেয়ার করতো,তুই তার বড় প্রমান,লিংক লাগ্লে বলিস",1,celebrity
বাইনচুত তুই একটা দালাল। শুয়োরছানা কোথাকার। তোরে সামনে পাইলে তোর মুখে হড়হড় করে বমি করে দিতাম।,1,celebrity
তুই একটা সুয়ারের বাচ্চা,1,celebrity
"হালার পুত কানা বুদ্ধি জীবি,দিনে  লুট খুন ঘুম চোখে দেখেনা,রাতের  বেলায় জামাত বিএনপি পায়ু দিলে কুকুরের মত ঘেউ ঘেউ করবে",1,celebrity
তুই ঘুমা। তোর মতো ষাড়েঁর ছায়াও জানি এই প্রজন্মের উপর না পরে🚦🚦⛔🚫🚫,1,celebrity
জাফ্রিলবাল ষাড়কে দেখলে কিংবা নাম শুনলে হড় হড় করে বমি করে দিতে ইচ্ছা করে,1,celebrity
#চে## বা#গুলা খুব শিঘ্রী কাটবো।।।আমরা একাই কাটতে পারি✌✌✌👊👊👊 #আপনি ঘুমান,1,celebrity
বাইঞ্চোদটার নুনুভুতি কেবল জেগে উঠেছে!,1,celebrity
#ষাঁড়_জাফইররা মশারির ভেতর থেকে বাহির হয়েছে...... সবাই সাবধান,1,celebrity
"চেতনার #মাদারচোদ,, এইবার তুই কোথায় ছিলি?,  ১৬ কোটি মানুষের সাংবিধানিক অধিকার কেড়ে নিলো তাও টু শব্দটা ও করলি না।। তোদের জুতা দিয়ে মারতে মন চায়।",1,celebrity
পাক্কা বোকাচোদা,1,celebrity
তুই চিটিং!,1,celebrity
এই সাউয়ার বেটার পুটকি মারার প্রয়োজন!,1,celebrity
স্যার কি তোরার মাইরে চুদছে??? খানকি মাগী চুদমারানির পোলা মাইয়ারা।,1,celebrity
গাধার বাচ্চা জাফর ইকবাল,1,celebrity
জারজ ও রাজাকারের বাচ্চারা লিখা না পড়েই কমেন্ট করা শুরু করছে। অশিক্ষিত ছাগলের কুলাঙ্গাররা উনি যে বিএনপির ইশতেহার রে ফেইল দিসে এটা নিয়ে কিছু বললি না খানকির বাচ্চারা।,1,celebrity
৭১- এ গর্তের ভেতরে লুকিয়ে এখন যারা মুক্তিযুদ্ধের গল্প শোনায় তারা গর্তজীবী- গর্তযোদ্ধা।তাদের মুখে মহান মুক্তিযুদ্ধের কাল্পনিক গল্প শোনা বোকামী। তাদের কে স্যার বলে ডাকা ন্যাকামি। জাফর আর মীর জাফর এক গোয়ালের দুষ্ট বলদ।এরা বাঙালির জন্য ব্রিটিশ আমল থেকে বিপদজনক।,1,celebrity
"আরে শয়তানের বাচ্চা তুই রাজাকারের বাপ সেটা তোর পোস্ট পড়েই বোঝা গেল। অমানুষের বাচ্চা, তোর মা বেশ্যা মুইত্তা যখন ছাত্রদেরকে রাজাকারের বাচ্চা বলে গালি দিল তখন কোথায় ছিলি শয়তানের বাচ্চা? আসল কথা হল পাকিস্তানেত রাস্তাঘাটে কোন কুত্তার বহুগামিতার মাধ্যমে তোর জন্ম হয়েছে শয়তানের বাচ্চা",1,celebrity
"....266 খানকির পোলা  নাস্তিক....মরার আগে ভালো হ,",1,celebrity
কুও্ওা দিয়া ফোন মারান উচিৎ 😈😝,1,celebrity
কুত্তে কা ধুম কাভী সী'ধে নাহী হোতাহে!!😜😜,1,celebrity
হালারপুরে জুতাদি ভাইরায়া হের মুছের গল্লা পালাইয়া দেওন দরকার।,1,celebrity
তুই হইলি একটা দালাল ছাগল,1,celebrity
"এই রকম ছাগলামী না করার চাইতে ঘুমান মিয়া, যতসব আতেল",1,celebrity
কুতা,1,celebrity
"কিরে তুই না, মরে গেল, একন আবার কই থাকি আইলে বেইনচুদ",1,celebrity
তোমারে কেউ চোদেনা.....??? ফাফর চ্যাটবাল...!,1,celebrity
আপনার বালছাল মার্কা পোস্ট না পড়েই সোজা কমেন্ট বক্সে বিনোদন নিতে চলে এলাম! যা মজা নেবার এখান থেকেই নিব! 😂,1,celebrity
"এই গরিব! সার কে নিয়ে এত কমেন্ট এর কি আছে। খাও তো শুটকি, আর ** পেত্নি। যাও তোমরা মদ খাও, আর সারকেও খাইতে দাও। মদ খাইলে বুদ্ধি হবে। :)",1,celebrity
দূর হ্লার পো,1,celebrity
"শুয়োর এর বাচ্ছা জাফর ইকবাল,,।।",1,celebrity
চৈতালি চুদে দিয়ে হাত তালি,1,"Meme, TikTok and others"
এই জানোয়ারের ফাশি চাই,1,"Meme, TikTok and others"
এই হারামীর বাড়ি কইকেউ পারলে ঠিকানা দেনএই কুত্তারে আমি খুন করবো,1,"Meme, TikTok and others"
খানকির পোলা তোরে রাস্তায় পেলে লেংটা করে তোরেই চুদমুবাইনচোদ,1,"Meme, TikTok and others"
সেফাতকে কেহ গালি দিলে আমার রক্ত গরম হয়ে জায় ও আমাদের রাত দিন ঘন্টা আমাদের বাড়ি ঘর পাহারা দেয় আমাদের বাড়ির কুত্তার নাম সেফাত এজন্য,1,"Meme, TikTok and others"
চোদানীর পোলা,1,"Meme, TikTok and others"
বেয়াদব জানোয়ার উনার হাত পা কেটে ফাশি দেন,1,"Meme, TikTok and others"
চোচড়িতোমার জায়গা তো এখন অপু বিশ্বাস দখল করে নিয়েছে দুদিন আগে দেখলাম,1,"Meme, TikTok and others"
সুচির গুদে তাজা মাল ফেলতে চাই,1,"Meme, TikTok and others"
সোনা খারা হয় মাদারি,1,"Meme, TikTok and others"
এখানকিরপোলা,1,"Meme, TikTok and others"
শালাকে ফাঁসি দেয়া হক,1,"Meme, TikTok and others"
এইশালিগোকইথেদইরানিয়াআইছে,1,"Meme, TikTok and others"
তুই একটা চুদ মারানি নডি,1,"Meme, TikTok and others"
চ্যানেল এডমিন তোর মা কে কাও চোদে,1,"Meme, TikTok and others"
মাগী তোর গূদে অচিলা বাশ ঢুকানোর খুব দরকার,1,"Meme, TikTok and others"
জাকীর নায়েক একজন পাকা খানকীর ছেলে,1,"Meme, TikTok and others"
কিরে সেফুদা এতো রাগ কেন শালা নাস্তিক,1,"Meme, TikTok and others"
খানকিটাকে পেলে পিটিয়ে মেরে ফেলতাম,1,"Meme, TikTok and others"
কুত্তারে পাইলে জবাই দিতাম,1,"Meme, TikTok and others"
এই খানকির যে যেভাবে পারেন গালি দিয়ে যান,1,"Meme, TikTok and others"
ও তো কুত্তার চেয়ে খারাপ ওকে জোবাই করা উচিত,1,"Meme, TikTok and others"
তোর মা আর তোর বাপ মনে হয় শুটকি দিয়া বেলা ভাত খাইত তাই তোর মত একটা শুয়রের পুটকির লাহান মোটা খাসি পয়দা করসে তুই আসলেই বেজন্মা তুই নিজেও জানস ওইটা মদ খা আর নিজের পুটকি নিজে মার শালা খানকির পোলা,1,"Meme, TikTok and others"
সালা পাগল,1,"Meme, TikTok and others"
ওকে ফাসিতে ঝুলিয়ে মারা দরকারওর মতো সন্তান জন্মের আগেই মেরে ফেলা দরকারআমার মনে হয় কোন প্রকৃত মোসলমানের বাচ্চা এরকম কোন জগন্য কাজ করতে পারে না হিন্দু কুত্তার বাচ্চায় এরকম খারাপ কাজ করতে পারেআমি জানি না ইন্ডিয়াতে কীরকম বিচার হয় কিন্তু আমার বাংলাদেশের কোন জায়গায় যদি আমার সামনে এরকম ঘটনা ঘটতো তাহলে ওই কুকুরের হাত কেটে ফেলে দিতাম,1,"Meme, TikTok and others"
সালায় বলে নায়ক হা হা,1,"Meme, TikTok and others"
তুর মাগি,1,"Meme, TikTok and others"
ফাসি চাই প্রিয়া সাহা খানকির,1,"Meme, TikTok and others"
দেশে আই তো তোর মার হেডা দিয়ে তোরে ডুকাই দিমু খানকির হোলা,1,"Meme, TikTok and others"
হারামি মুদি অমিত শাহ শয়তান দুটো কবে দুনিয়া থেকে যাবি তোদের ঠিকানা তো জাহান্নাম,1,"Meme, TikTok and others"
এর ফাঁসি চাই এই মেয়ে শয়তান,1,"Meme, TikTok and others"
তুর সোনাটার একটা ছবি দে সোনা ঠিক আছে কিনা দেখি ঠিক থাকলে টাকা পাবি,1,"Meme, TikTok and others"
ট্রাম্প একটা পাগলতাই যদি এই ব্যাপারে নাক গলাতে পারে তানোরে মেক্সিকো সীমান্ত দিয়ে অনুপ্রবেশ কারী রুখলো কেনোআর ওই ইমরান খান কে তো গুলি মারা উচিত,1,"Meme, TikTok and others"
চোখে পানি ধরে রাখতে পারলাম না আল্লাহ্‌ এই রকম সন্তান কারো ঘরে দিও না আর তাদের দিয়েছো সেই সব কুলাঙ্গার সন্তানদের নিশ্চিহ্ন করে দাও এই রকম সন্তান যে জাতির ঘরেই হোক না কেনো,1,"Meme, TikTok and others"
আসলে এই জন্য আমাদের দেশে ভিক্ষুক বেশিনইলে সেই মহত লুক অনেক আছেন তারপরও তারা চুপকরে থাকে এই জন্যই কারন তারা দুধ ভাতদিয়ে কাল শাপ পুশতে চান্না,1,"Meme, TikTok and others"
ওই জানোয়ার ক তিলে তিলে মারা দরকার তোর মরণ হয় না কেন রে যে বাবা তোকে মানুষ করলো তাকে মারছিস মনে রাখিস তোকেও এমন দিন দেখতে হবে আর ওর বৌ তাকে ধরে এ বেঁধে মারো,1,"Meme, TikTok and others"
চুদবো,1,"Meme, TikTok and others"
এই জারুয়ার বাচ্চাকে প্রশ্রয় দেওয়া ঠিক না এর জন্য আনেক মানিষ অসহ্য ফিল করে আর এই মাগির বাচ্চা আনাদের ধর্ম নিয়ে বারাবারি করছে একে আর প্রশ্রয় দেয়া ঠিক নাহ্ এই মাগির বাচ্চা নামাজ নিয়ে উল্টা পাল্টা কথা বলবি না খাংকির পোলা,1,"Meme, TikTok and others"
এই কোততার বাচ্চারে জেনতা কবর দেন,1,"Meme, TikTok and others"
এই কুকুর কে এমন মার দেওয়া লাগবে সারা জিবন জেন চেলেনের মতো ঝিরঝির করে,1,"Meme, TikTok and others"
হারামজাদা টাকে কেলাতে হয় খুব,1,"Meme, TikTok and others"
জানোয়ারের বাচ্চা জাহান্নামে ও জায়গা হবে না তোর,1,"Meme, TikTok and others"
খানকিমাগী আর খানকির পোলা এই কারণে এই সবগুলি মিডিয়ার সামনে ইউটিউব এ মনি প্রচার করবে ভালো মানুষের মেয়ে এবং ছেলে বলে এইগুলি গোপনে চিকিৎসা করে,1,"Meme, TikTok and others"
ওই খানকির ছেলের দুই হাত কেটে দেওয়া উচিৎ,1,"Meme, TikTok and others"
এই হল বাংলার নায়ক বাল ছাল এই নায়ক হলে মানুষ ফিল্ম দেগবেনা,1,"Meme, TikTok and others"
খানকির পোলার ফাঁসি চাই চোদ মারানির পোলাতরে পাইলেরে কীজে করতাম,1,"Meme, TikTok and others"
ভালো হয়েছে শালা ধরে নিয়ে গেছে যে বাপ মা জনম দিলো তাদের গায়ে হাত দেওয়া হাত ভেঙে রেখে দিতে,1,"Meme, TikTok and others"
মিথিলা একটা বিশ্ব খানকি,1,"Meme, TikTok and others"
এই কুকুর ছেলে কে পেলে জুতা পিটিতাম ভিডিও দেখে চোখের পানি আটকাতে পারলাম না,1,"Meme, TikTok and others"
মাগির পোলারে কেউ আমার কাছে আইনা দে,1,"Meme, TikTok and others"
মাদারের সুদ কে ফাঁসি দেওয়া উচিত,1,"Meme, TikTok and others"
সালার পোলা সালা,1,"Meme, TikTok and others"
ওর পুটকি দিয়া গরম অান্ডা ঢালো তাহলে এরকম আর কেউ করবেনা,1,"Meme, TikTok and others"
ওই শালা ওর ছেলের মার খাবে,1,"Meme, TikTok and others"
বেস্সার বেটার বাড়ি কৈ,1,"Meme, TikTok and others"
কুত্তার বাচ্চারে বাচায় রাখছে কেন এখনো,1,"Meme, TikTok and others"
চার বাল পাকনা,1,"Meme, TikTok and others"
সালারপুত সিনামার ডাইলগ দিতাছে গরুর দাম না বলেডালা সিনামা প্রচার করতে আইছে বাইনচোদ,1,"Meme, TikTok and others"
সত্যি প্রধানমন্ত্রীর হলো জানোয়ার,1,"Meme, TikTok and others"
তোর তো করতি ইচছা করছে,1,"Meme, TikTok and others"
শালাকে লাথি মারা উচিতজনসম্মুখে মারা উচিত,1,"Meme, TikTok and others"
ময়ুরির দুধ আগের থেকে এখন আরো বড়ো হইছে,1,"Meme, TikTok and others"
এই শুয়োরের বাচ্চা তোর মানুষের চামড়া আছে তোকে যদি সামনে পেতাম যে হাত দিয়ে চড় মেরেছিস তোর হাত কেটে দিতাম,1,"Meme, TikTok and others"
ও আল্লাহ তুমি কোথায় এই জানোয়ারের হেদায়েত দাও আল্লাহ এর বিচার দুনিয়াতে দেখাও,1,"Meme, TikTok and others"
খানকির পোলার চাসি চাই বোয়ের চামচা৷ চাকড়ের বাচ্চা তরে পাইলে মাইরা কুকুরে দিয়ে খাওয়াত জানোয়ার,1,"Meme, TikTok and others"
এদের উল্টো করে মাথা পানিতে ডুবিয়ে পেটানো উচিৎ,1,"Meme, TikTok and others"
হারামজাদার হাত দুইটা কেটে ফেলাই হবে সঠিক বিচার,1,"Meme, TikTok and others"
তোর মাইরে চুদি বুস্কির পোলা,1,"Meme, TikTok and others"
তাহার সব চেয়ে বড় পরিচয় সে একজন পাগল,1,"Meme, TikTok and others"
আরে খানকী মাগী বেশ্যা মাগী বেশ্যা তোর বাবা হলেন তোর ভাই,1,"Meme, TikTok and others"
বাল কে এই রানুওতো একজন পাগল একজন সাওতাল আদীবাসী মুখে ঘা ওর মাথা উকুনের কারখানাওতো ভিখারী গান গেয়ে খেতো ওকে ওর নিজের মেয়েই চিনতে পারেনা আবার বলছে আমি তো জানি আমি কে দুমুঠো যে কিনা খেতে পেতনাতার আবার অহংকারী কথা,1,"Meme, TikTok and others"
জাতীয় নুচ্চা শালায়,1,"Meme, TikTok and others"
সাকিব কিভাবে বুবলি মাগির পাল্লায় পড়ে আপু কে ভুলে গেলে আমি অপু আপু কে অনেক অনেক ভাল বাসি,1,"Meme, TikTok and others"
এই কুত্তার বাচ্চা কে ফাসি দেওয়া হোকযেই মিষ্টির জন্য আজ এই ছেলে বাবা কে মারছে একদিন ছেলের খুশির জন‍্যছেলের মুখে হাসি ফোটানোর জন‍্য বাবা শরীরের রক্ত পানি করছেফাসি দেওয়া হোক জানোয়ার এর বাচ্চারে,1,"Meme, TikTok and others"
শাকিব একটা পাকা মাদারি,1,"Meme, TikTok and others"
সাহস থাকলে বাংলাদেশে আয় মাগার পূলা,1,"Meme, TikTok and others"
আগে ছিল খানকি এখন হয়েছে বেশ,1,"Meme, TikTok and others"
নামাজকে খারাপ কথা বলোছ কুত্তার বাচ্চা,1,"Meme, TikTok and others"
খানকির পোলা ইসলাম নিয়া কথা কইলে পাছার মদ্ধে মদের গ্লাস ভইরা দিমু নট্টির পুলা,1,"Meme, TikTok and others"
মোদি ও অমিতশা দুই হালায় দেসের গাদ্দার ফাঁসি চাই,1,"Meme, TikTok and others"
ছালা একটা ছুয়ার রে দাদা,1,"Meme, TikTok and others"
শালা একটা কুত্তা,1,"Meme, TikTok and others"
এই কুত্তা কে জবাই করা উচিৎ🥶🥶,1,"Meme, TikTok and others"
গলাটা নুসরাত মাগির মত,1,"Meme, TikTok and others"
খানকি মাগি মিথ্যাবাদী তোর তুরস্কের গুদ মারি,1,"Meme, TikTok and others"
ফাঁসি চাই কুত্তা প্রদীপ বিশ্বাস নামক হারামিটার,1,"Meme, TikTok and others"
খানকি এসব বালছাল খবর কোথায় পাস তোর মাথায় কিছু আছে বেশ্যা মাগি,1,"Meme, TikTok and others"
এই শালীর তো মুখ বড় নিচেরটা টা আরো বড়,1,"Meme, TikTok and others"
জানোয়ারটাকে কুকুরের মত মারা দরকার,1,"Meme, TikTok and others"
সালার হাত কেটে দেওয়া হোক,1,"Meme, TikTok and others"
এর বিচার না হলে এই হিন্দুর গুষ্টি চুদে দিবো,1,"Meme, TikTok and others"
সালাকে ধরে মার,1,"Meme, TikTok and others"
এই শয়তানের বাড়ি কই ওর মত সন্তান থাকার চেয়ে না থাকা ভালো,1,"Meme, TikTok and others"
মিথিলা একজন বেস্সা মেয়ে৷৷৷৷৷,1,"Meme, TikTok and others"
খানকির পোলা তোরে মথ খাওয়াইয়া কুকুর দিয়া চোদামু,1,"Meme, TikTok and others"
বরিশালের মেয়েরা পুরাই পগল,1,"Meme, TikTok and others"
ওর গোয়ায় বাশ দে,1,"Meme, TikTok and others"
শুয়োরের বাচ্চা যে বাবা তোকে মানুষ করলো তার গায়ে তুই হাত দিলি আল্লাহ তায়ালা যেন তোর দুই হাত পচিয়ে নষ্ট করে দেয়,1,"Meme, TikTok and others"
খানকির পোলারে মাদার চুদকে জবাই কর দেশে কি আইন নাই ফাসি চাই,1,"Meme, TikTok and others"
অপু ভূয়াবেয়াদ ফালতু মহিলা অচল পয়সা খানকী মাগী,1,"Meme, TikTok and others"
সুচির ফাঁসির আদেশ হোক আর মোদি কুততার মরন হোক,1,"Meme, TikTok and others"
মুসলমানদের কথাই কথাই জংলী বলছ তরা পাইছত কি তরা জংলী তরে কি পুটকি মারছে খানকি মাগি,1,"Meme, TikTok and others"
কুওার বাচ্চাকে ফাসি দেওয়া উচিত যেই বাবা তার জীবনকে বাজি ধরে সন্তান কে মানুষ করে তার গায়ে হাত আল্লাহ সহ্য করবে না গজব পড়বে,1,"Meme, TikTok and others"
ওরে ত হিজরার মত লাগছে সালি মাগি,1,"Meme, TikTok and others"
সুয়ার টার চামরা ছিলে লবন আর বোমবাই মরিচ গোল মরিচ জতো প্রোকার মরিচ মেখে দেওয়া উচিত ওকে জদি আমার সামনে পেতাম তা হলে কুচি কুচি করে কাইটা ফেলাইতাম কুত্তা টাকে,1,"Meme, TikTok and others"
মিথিলা একটা খানকিমাগী,1,"Meme, TikTok and others"
এমন কুলাঙ্গার যেন কারো ঘরে না জন্মায়,1,"Meme, TikTok and others"
মাদারীর বেটি মাত পাকাও এডমিনরে রিকশাচালক চুইদা পেটবানাই দিছেরে,1,"Meme, TikTok and others"
এই শালারে ক্রসফায়ারে দেওয়া হয় নাই কেন,1,"Meme, TikTok and others"
বাংলাদেশ হলে ঐ কুলাঙ্গার কে সবাই পিষে ফেলতো সে যে ধর্মেরই হোক না কেন,1,"Meme, TikTok and others"
তোর মাং ফাটাবো রে শালা,1,"Meme, TikTok and others"
সালিকে আবার ভিখারি বানান,1,"Meme, TikTok and others"
এই পাগল আবার কই থেকা আইলো,1,"Meme, TikTok and others"
ও যে হাত দিয়ে ওর বাবাকে মেরেছে সেই হাতের কবজি কেটে নেওয়া উচিওবাইন চোদ কোথাকার,1,"Meme, TikTok and others"
কুত্তার বাচ্চারে দুনিয়া থেকে উপরে পাঠায় না কেন,1,"Meme, TikTok and others"
এসব সন্তানের উপর আল্লাহর তরফ থেকে গুজব পরা উচিত ছি ছি ছি এ সন্তান নাকি জানোয়ার 🤔🦗🦀,1,"Meme, TikTok and others"
মাগীর পুত তুই ষেয়ে দেখে আয়ছিস,1,"Meme, TikTok and others"
মাগী মরার চিন্তা কর,1,"Meme, TikTok and others"
তুই শালা কতো বড় যুবক বাবা কে মারছিস এর ফল একদিন পাবি,1,"Meme, TikTok and others"
শুয়রটা কে গলায় পাড়াদিয়ে বুঝিয়ে দেওয়া উচিত বাবা মা কি জিনিস শুয়রের কান্ড দেখে মনে হলো শুয়রটা রোজ এই কাজটা করে সাথে তার বৌও জড়িত এই শুয়রের চরম শাস্তি হওয়া উচিত যাতে করে কেউ এরকম করতে সাহস না পায়,1,"Meme, TikTok and others"
তর মাইয়ারে চুদি হালার বুইড়া,1,"Meme, TikTok and others"
চোদানি,1,"Meme, TikTok and others"
চুদার অভাব মাগী র,1,"Meme, TikTok and others"
এই বেজন্ম্মা কে আমার হাতে কেউ ঘন্টার জন্য তুলদিক ওর শরিরে সব রক্ত পাছা দিয়ে বার করে দেবো,1,"Meme, TikTok and others"
তুই ত শালা পাগল,1,"Meme, TikTok and others"
ওই শালা কে মারতে মারতে মেরে ফেলা দরকার,1,"Meme, TikTok and others"
ওই খানকির পোলা বলে কি তোর মারে আসলে কি তোর মার সোনা পাক করেছে খানকির পোলাকে ওই খানকির পোলা আমার মারেচুদছিস খানকির পোলা হিজলা দের মত পড়ে পক পক করে খানকির পোলা না,1,"Meme, TikTok and others"
এই শালারে কুপাইয়া মারা দরকার,1,"Meme, TikTok and others"
আমি হলে খানকির ছেলের হাত কেটে ফেলে দিতাম,1,"Meme, TikTok and others"
তোর কানের তলায় কোশে একটা মারবো চুদানির পুলা তুই ধমরে গালি দিস,1,"Meme, TikTok and others"
মালুর যাতের কোন বুক পিট নাই,1,"Meme, TikTok and others"
এই সালায় পাগল,1,"Meme, TikTok and others"
যে মাগী এই সংবাদটা পাঠ করছে তার ভোদা দিয়ে আগুন আগুন গরম রড ঢুকিয়ে দাও সবাইএই অনুষ্ঠানটি যে প্রচার করছে তারা সবাই ব্লাডি বাস্টার্ডসান অফ বিচফাকিং অফ ডগএনিমি অফ ইসলাম,1,"Meme, TikTok and others"
একে জ্যান্ত কবর দেওয়া দরকার আল্লাহ এর জীবনে যেন মাফ না করে,1,"Meme, TikTok and others"
এই মানুষ না জানোয়ার,1,"Meme, TikTok and others"
এই ইহুদি মাগিকে সবাই আঝড়া বাঁশ দিন,1,"Meme, TikTok and others"
সালারে পাইলে আমি ওই মাইর দিতাম,1,"Meme, TikTok and others"
এর পুটকি বায় রড ডুকিয়ে রাস্তায় রাখা উচিত,1,"Meme, TikTok and others"
জারজ সন্তানের খবর আসে মিডিয়ায় কিন্তু ইসলামিক কোন খবর আসে না মিডিয়ায়,1,"Meme, TikTok and others"
কুকুরের পেটে ঘি ওজম হনা মাগি একটা কুকুর,1,"Meme, TikTok and others"
শালা শুয়ার,1,"Meme, TikTok and others"
ওটা একটা কুত্তার বাচ্চাছি ছি ছি,1,"Meme, TikTok and others"
চোদছে নি আরও ভালা কইরা ছুদে জান ওইলারে কানকি মাগি রে,1,"Meme, TikTok and others"
খানকিমাগী ফালতু বকিস কেন,1,"Meme, TikTok and others"
এই কুলাঙ্গারকে কেউ মেরে ফেলতে পারলে আমার সবকিছু বিক্রি করে তাকে পুরস্কার দিতাম আহারে এই বাপ যদি জানতো তার ছেলে বড় হয়ে এই হবে তাইলে সেই রাতে বীর্যটুকু লুঙ্গিতে ফেলেই শুকায়ে ফেলতো,1,"Meme, TikTok and others"
কুততার বাচ্চা কে মেরে ফেলুন,1,"Meme, TikTok and others"
ওটা ছেলে না জানোয়ার কুকু্র একটা,1,"Meme, TikTok and others"
মোদী কুত্তার বিপক্ষে,1,"Meme, TikTok and others"
ববলিকে জুতা মারো যে অনের সংসার ভাংগে তাকে জুতা মারা দরকার,1,"Meme, TikTok and others"
মিন্নি মাগিরে প্রাকাশে কুপিয়ে হত্যা করা হউক,1,"Meme, TikTok and others"
দুর মাগি,1,"Meme, TikTok and others"
শালাগো ধোন গোরার থেকে কেটে দে,1,"Meme, TikTok and others"
এ কুত্তার বাচ্চা,1,"Meme, TikTok and others"
কুকুরের বাচ্চা তোর গুষ্ঠি বেশ্যা দা জানোয়ার ইস্লাম নিয়ে কটুক্টি করস জারোজের বাচ্চা,1,"Meme, TikTok and others"
খানকির পোলা তো মায়রে চুদি বোকাচোদা বুরা চুদা আমাদের দেশ ভালো তোর ভোদায় পাগল কুকুর চুদবেনা চুদা চুদা মারাস চুদার বল আছে বোকা চুদা তোমায়রে চুদিনা ‌,1,"Meme, TikTok and others"
ওই বোকাচোদা ছেলেকে ব্লেড দিয়ে কেটে নুন লঙ্কা দিয়ে দিন ফেলে রাখা উচিত,1,"Meme, TikTok and others"
তুই একটা বড় মাগি,1,"Meme, TikTok and others"
কুলংঙার ছেলে আর নষ্টা বউ জারত বউ কোন মা পেটে নিয়েছে এমন বউ কে তুই তোর বাবার গালে গায়ে চর মারচত তোর হাতটা যেনো পচে গলে ধংষ হয়ে যায় ওর কঠিন সাজা চাই সোয়ারের,1,"Meme, TikTok and others"
সালার পুতেরে কসাই আট দশটা চবা মার,1,"Meme, TikTok and others"
কিছু বলবো না ভিডিওটা দেখে চোখের পানি আর ধরে রাখতে পারিনা এই জানোয়ারের বিচার যেন অতি শীঘ্রই উপরওয়ালা করে,1,"Meme, TikTok and others"
ফেনীর মাগী ইমো নাম্বার ডালিয়া,1,"Meme, TikTok and others"
এর দুইটা হাত কেটে দেওয়া হোক,1,"Meme, TikTok and others"
এই কুত্তাটাকে কেটে টুকরো টুকরো করে বস্তায় ভরে ঝুলিয়ে রাখা উচিত,1,"Meme, TikTok and others"
পাগলে কিনা বলে ছগলে কি নাখায়,1,"Meme, TikTok and others"
এই সেফু কে না মেরে খানকির পু এই ইউটুবার কে ধরে জবাই করা দরকার কারন তাদের ব্যবসা বড় করার জন্য এসব ভিডিও ভাইরাল করে,1,"Meme, TikTok and others"
পা‌শে বউ না কেউ দাড়‌ি‌য়ে দেখ‌ছেতা‌কেও শাস্ত‌ির অাওতায় অানা হোকপ্র‌তি‌বেশীরা হি‌জরা না‌কি শালা রে থাপরাইয়া দাঁত গুলা ফালাইয়া দেওয়া উ‌চিত কুলাঙ্গার শালা,1,"Meme, TikTok and others"
মাও মাগি মেয়েও মাগি,1,"Meme, TikTok and others"
ওরে ফাসি দেওয়া হক সালা কুতা,1,"Meme, TikTok and others"
খানকি বোদায় বাঁশ ডূকিয়ে দিলে হয়তো,1,"Meme, TikTok and others"
লাব কি হে হলো মাগি,1,"Meme, TikTok and others"
হালা আজও কথা বলতে যানেনা সে নাকি নায়ক এটা শুধু বাংলাদেশে চলে আবাল কোথাকার,1,"Meme, TikTok and others"
ওই খানকির পুলার বাড়ি কই আমরা যদি থাকতাম তা হলে যে কি হতো আল্লাহ জানে,1,"Meme, TikTok and others"
চোখ দিয়ে পানি এসে পড়ল যে বাবা জন্ম দিছে তাকে এইভাবে মারতে পারল জানোয়ারটাতা আবার ওর মাকে মিষ্টি খাওয়াইচে বলেছ আল্লাহ তায়ালা জানোয়ার টাকে শাস্তি দাও,1,"Meme, TikTok and others"
তোরে সামনে পাইলেহাত পা কেটে ফেলায় রাখতাম রে কুলাংগারতোরে জন্ম দিছে রে উনিজানোয়ার তুই একটাতোরে কই পাবো রে কুত্তা,1,"Meme, TikTok and others"
শুয়রএর বাচা তুই আমার সামনে পড়িস না তুই জুদি আমার সামনে পড়স তা হলে বাংলাদেশ সরকার আমাকে ফাসিদিবে,1,"Meme, TikTok and others"
খাকি মাগি তুর মিয়েকে দি,1,"Meme, TikTok and others"
এই কুকুরের বাচ্ছা কে ফাসি দেয়া হক,1,"Meme, TikTok and others"
তোরে গুদে বোম মারবো,1,"Meme, TikTok and others"
এই জানুয়ারের বাচ্চার ফাঁসি দিতে হবে,1,"Meme, TikTok and others"
এমন ছেলেকে কুত্তা দিয়ে খাওয়ানো উচিত,1,"Meme, TikTok and others"
পুসির সাইজ কত কার,1,"Meme, TikTok and others"
এই তো রেট কতো,1,"Meme, TikTok and others"
এ শালার বাংলাদেশে পালি মাইরে পুতে ফেলায় দিতাম,1,"Meme, TikTok and others"
কুতা মুখো মহিলা ফকিনি বাচ্চা হাতে পেতেট দিয়ে কুতা খেতে দেয় সালা পাগলীর বাচ্চা,1,"Meme, TikTok and others"
তোর গোষ্ঠীকে শালি,1,"Meme, TikTok and others"
নাস্তিচ কুত্তার বাচ্চাশুওরের বাচ্চা তোর ফাসি চাই,1,"Meme, TikTok and others"
জানোয়ারের বাচ্চা একটা ওরে জনসমোক্ষে গলা কেটে ফেলা উচিত যে বাবা জন্ম দিছেসে বাবারই উচিত চাক্কু দিয়ে জানুয়ারের গলা কাটা,1,"Meme, TikTok and others"
এই মালাউন রঞ্জন গৈগ নিজের অপকর্মের অপরাধ থেকে বাঁচার জন্যই এ বিতর্কিত রায় দিয়েছে,1,"Meme, TikTok and others"
গুদ লাগে ধন দেখাছিস,1,"Meme, TikTok and others"
সালা জানোয়ার,1,"Meme, TikTok and others"
শালি দুর হ,1,"Meme, TikTok and others"
বালের দেশের বালের রায়,1,"Meme, TikTok and others"
লোক টাকে হারামি হারামি লাগে৷,1,"Meme, TikTok and others"
চাইনা আমরা মোদী সালা,1,"Meme, TikTok and others"
নাইকার মারে চুদি,1,"Meme, TikTok and others"
পৃথিবীতে এর চেয়ে জঘন্য দৃশ্য আর হতে পারে না যে ছেলে হয়ে বাবার গায়ে হাত তুলতে পারে সে ছেলে নামের একটা জানোয়ার ছাড়া পৃথিবীতে তার আর কোন নাম হতে পারে না বাবামা যাই হোক না কেন তাদের উপরে কিভাবে হাত তুলে একটা পশ আমরা নিঃসন্দেহে ওই পশুর ফাঁসি চাই,1,"Meme, TikTok and others"
খানকির পোলারে পাইলে,1,"Meme, TikTok and others"
ঐ শালারে ফাঁসি দেওয়া উচিত,1,"Meme, TikTok and others"
কুত্তার বাচ্চাকে জবই করা হোক,1,"Meme, TikTok and others"
এই সকল জানোয়ারকে সুলে ছড়ানো হলে খুশি হব,1,"Meme, TikTok and others"
শালা ভালো মানুষ নাবহু খারাপ,1,"Meme, TikTok and others"
সোন শালি তোর দেশ কে দেখ ফালতু খবর বলিস না তোর দেশে মহিলা রা সৌদি আরবে গিয়ে যৌনো দাশি হচ্ছে কেন রে মাগি সেটা দেখ আগে বুঝলি ভারতে পোদের পিছনে লাগিস না শালি তোর খাওয়া কোনো কাজ নাই ফালতু খবর বলিস তোর দেশকে আগে দেখ,1,"Meme, TikTok and others"
ও মানুষের ভিতরে পরে না,1,"Meme, TikTok and others"
ছামার পো হালার পোলা খারাপ চোদা,1,"Meme, TikTok and others"
এমন ছেলেকে মেরে ফেলা ভাল,1,"Meme, TikTok and others"
পাগলি মাথায় কান্সার এই অনুপ্রবেশ কারির আপনারা একে ইরানে বিয়ের ব্যাবস্থা পরুন,1,"Meme, TikTok and others"
নডিপুতেদিন,1,"Meme, TikTok and others"
খোদার কছম খানকির পোলারে যদি পাইতাম,1,"Meme, TikTok and others"
কুত্তার বাচ্চা কে মেরে ফেলা উচিত,1,"Meme, TikTok and others"
এই কুলান্গার কে এমন শাস্তি দেওয়া হোক পৃথীবির আর কোন কুলান্গার যেন বাবামায়ের গায়ে হাত তোলার সাহস না পাই,1,"Meme, TikTok and others"
খানকির পোলার পাশি চাই,1,"Meme, TikTok and others"
এই রকম জানোয়ার ছেলেকে মানুষ করার থেকে একটা কুকুরকে মানুষ করা উচিত ছিল,1,"Meme, TikTok and others"
সালাকুত্তা মাদার চোদ জানোয়ার জারো তোর গুষ্ঠি ছাগলের বাচ্চা সরকার আইন কার বাল ফেলে,1,"Meme, TikTok and others"
ঐ মাগির ঘরের মাগিঅনুষ্ঠানের মাধ্যমে লোক সমাজে না বলে তোর আর তোর মায়ের স্তন ও বুদা বিষয়ে গোপন ভাবে ডাক্তারের কাছে বল,1,"Meme, TikTok and others"
সালারা তোদেরকে জুতা পেটা করা ওচিত আপডেট করে খবর বলিশ,1,"Meme, TikTok and others"
ওটা একটা কুত্তা মানুষ না,1,"Meme, TikTok and others"
ঐ সুকরের বাচ্চি তোর খবরের হেড লাইন থাকে একটা খবর থাকে কিছু অন্য এই গুলো বন্ধ কর,1,"Meme, TikTok and others"
হালায় ভুয়া নিউজ মারছে,1,"Meme, TikTok and others"
ফামিদা রহমানের গুদের বাল পেকেছে সেই খবর আপনারা যানেন,1,"Meme, TikTok and others"
মানুষ কুত্তার বাচ্চা কারন এই ভিডিওটা দেখলেই বুজা যায় অান লাইক দিছে এগুলা কুত্তার বাচ্চা,1,"Meme, TikTok and others"
ওরে খমা করা হবেনা ও একটা জানোয়ার,1,"Meme, TikTok and others"
এই কুত্তারে যদি আমি সামনে পাইতাম অফফফফফফফ ভাষায় কিছু বললাম না,1,"Meme, TikTok and others"
তোরে তেল ছারা চুদি,1,"Meme, TikTok and others"
হিজলা নায়ক,1,"Meme, TikTok and others"
এই শালীরাই বাংলাদের ফিল্ম জগতটা নস্ট করে গেছে ওদের আর এখন খাওয়া নাই,1,"Meme, TikTok and others"
এই কানকির পুত রে কুত্তা দিয়ে বার চোদানো দরকার,1,"Meme, TikTok and others"
আপু আপনার ব্রা কতো বলেন,1,"Meme, TikTok and others"
সালা আসলেই লুচ্চা,1,"Meme, TikTok and others"
তর দুদের চাইজ কত,1,"Meme, TikTok and others"
ফেইক নিউজ মাগী তোরে আমার গ্রামের পাগলা কুকুর দিয়ে চোদাবো,1,"Meme, TikTok and others"
তোমারভুদায়এতোএতোকামড়যেঘুড়ারধনদিয়একটানাপাচঘন্টাধরেচুদারদকার,1,"Meme, TikTok and others"
তোকে চুদার পক্ষে,1,"Meme, TikTok and others"
পাগল না কি লাইক কমেন্ট এইসব পাগল তুমি,1,"Meme, TikTok and others"
পুজা চ্যারি নাকি ক্লাস এ পড়ে তাহলে এতো ছোট মেয়ের সাইজ এতো বড় করলো কেওর তো বিয়েও হয় নাই 🤔🤔,1,"Meme, TikTok and others"
শালি কিসের শাকিব খানের কথা মেনে চলিস নিজের ছেলের জন্মদিনে স্বামীর পটো দিসনাই সেটার উত্তর আগে দে শাকিব খানের জারা শত্রু তাদের সংগে হাত মিলিয়ে চলা পিরা করিস তুইত শাকিব খানের ভাল চাস না,1,"Meme, TikTok and others"
খানকি কে আর কেমন লাগবে,1,"Meme, TikTok and others"
মাগির তুই জানিস জাকির নায়েক খুনে আছে সেই এখন মালয়েশিয়া আছে,1,"Meme, TikTok and others"
সাবিক খানকির হোলা,1,"Meme, TikTok and others"
কুতার বাচ্চারে ফাঁশি দেওয়া দরকার,1,"Meme, TikTok and others"
খানকির পোলার ফাসি চাই,1,"Meme, TikTok and others"
তোমার দুই হাতে জোর আছে আজ ছোট বেলায় তোকে জন্ম দিয়েই ভুল বাবা মা আর কি জানোয়ারের কর্মকাণ্ড দেখলে মনে হয় জন্ম দিয়াই ভুল এই ছেলে দুই হাত কাটা হোক,1,"Meme, TikTok and others"
হেডার পুত বাবা রে পিডা দেস,1,"Meme, TikTok and others"
ঐরকম খানকির ছেলেকে মাটিতে পুঁতে ফেলা উচিত ও যেমন ওর বাবাকে মারলো ওর ছেলে মেয়ে কিন্তু ওকেই ঠিক একইরকম হাল করবে,1,"Meme, TikTok and others"
তোক আর তোর মাক এক সঙ্গে চদিম মাগী,1,"Meme, TikTok and others"
চারাল এর পরিচয় এভাবেই হয়,1,"Meme, TikTok and others"
সাথে মাগিকে নিয়ে যেতে হয় পাসে দারিয়ে দেখছে খানকি যারা ছবি করেছো তাদেরকে ধন্য বাদ,1,"Meme, TikTok and others"
খানকি মাগি তোর ভুদাদিয়ে গরম ডিম ঢুকাইয়া দিবো,1,"Meme, TikTok and others"
হালা কুত্তার বাচ্চা তরে পাইলে আমি খুন করতাম আমি তরে জম্ম দিছে তারে মারলি তরে আমি গলা কামু তর লিঈ কাটমু,1,"Meme, TikTok and others"
শালা সিরাজগন্জের মানসম্মান মারছে,1,"Meme, TikTok and others"
নুডুস মাদারচোদ,1,"Meme, TikTok and others"
মাগি জবা,1,"Meme, TikTok and others"
শালি পাগল চোদা,1,"Meme, TikTok and others"
টাকা টা কোতাই পাঠাবো তুমার গুদের ভিতর ঠিকানা টা দাও মাগি,1,"Meme, TikTok and others"
এই সব শয়তান এর চলে যাওয়া ভাল হইছে কারণ ইয়াবাসহ অনেক কুকর্ম শিখাইয়া গিয়েছে,1,"Meme, TikTok and others"
ওরে সামনে পাইলে বোঝাইতাম এতে মানুষ না জানোয়ার ওকে ফাসি দেয়া দরকার,1,"Meme, TikTok and others"
শালা এজিদের বাচছা,1,"Meme, TikTok and others"
এই কুত্তার বাচ্চারে কঠিন সাজা দেওয়া হক,1,"Meme, TikTok and others"
শালারে পাইলে মুখে লাথি মারতাম,1,"Meme, TikTok and others"
মিন্নি তোমার কি হয় কালাত বোন নাকি মিন্নিত ছিল কারাপ মাগি জামাই রেকে কুনি নয়ন কে মিস্টি কাবায়,1,"Meme, TikTok and others"
নুচচা মাগি দূত দেখে বোঝা যায় আর ও যে সব ছবি করছে আর বললাম না থাক,1,"Meme, TikTok and others"
মুদি হলো কুকুর,1,"Meme, TikTok and others"
তোক কি মিনিন চদবা দিছে,1,"Meme, TikTok and others"
ভাই এটা হলো একাটা লুজ কেরেকট্টোর মহিলাকে ইন্টারভিউর নাম কোরে পাবলিকের সামনে নিজের লাভের জন্ন্যে মানহানীর চেস্টা করা হোচ্ছে কে এইরোকম কিছু মিম্ন প্রকিতি লোকেরাই তো বাংলাদেশের চলচ্চিত্রের পুটকি মেরেছিল যা এখনো সাদন হয় নাই,1,"Meme, TikTok and others"
কিছু কুকুরের বাচ্চা আছে এই ভিডিওর পক্ষ নিয়া কথা বলতেছে তাদেরকে অনুরোধ করা যাইতেছে পারলে আপনাদের জুতা মার্কা চেহারার একটা ছবি দিবেন আর সাথে ঠিকানা তাহলে সরা সরি গিয়েই কথা বলতে চায় হারামজাদারা এক কুকুর এর বাচ্চা বলছে আল্লাও নাকি ঠিক মতে চলেনা তার নাম দেখতে চাইলে আমার কমেন্ট গুলো দোখেন সালা মাদারি কি লিখছে এরে বলতেছি পারলে ঠিকানা দে তুরে বুঝাই দুধ কি ভাবে খারা করা যায় মাগির পু,1,"Meme, TikTok and others"
তোরসাইজ কতো মাগীতুই খানকি,1,"Meme, TikTok and others"
কুকুরের শরীর কেটে লবন আর মরিচ লাগানো দরকার,1,"Meme, TikTok and others"
কুলাঙ্গার পঙ্গু হয়েছে নাকি,1,"Meme, TikTok and others"
ওই মাগীহেড লাইনের সাথে তোর কথার মিল নাইএর জন্য তোরে প্রথমে পুরা ল্যাংটা কইরা তারপর তোর দুই ঠ্যাং ফাক কইরা ইন্চি দোন পুরা ঢুকাইয়া চুদতে চুদতে তোর ভোদা ফাটাইয়া দেয়া উচিততুই একটা খানকির বাচ্চাএর জন্য উল্টা পাল্টা নিউজ করিস মাগী কোথাকার,1,"Meme, TikTok and others"
হাচিনা শয়তান ভোট চুর,1,"Meme, TikTok and others"
তুই জানয়ার,1,"Meme, TikTok and others"
শালা ভালো মানুষের ঘরে যে জানোয়ার জন্ম হয় এই সালাই তার জলজ্যান্ত প্রমান,1,"Meme, TikTok and others"
মানুস পারে এ ভাবে বাবাকে মারতেও পশুর চেয়েও খারাপ,1,"Meme, TikTok and others"
এই খানকির পোলারে কি বলবো আর,1,"Meme, TikTok and others"
সালা কুত্তা বাবার মনটা বুজেনা,1,"Meme, TikTok and others"
ঐ বেশ্যা কই ওদের র্পন ছবি,1,"Meme, TikTok and others"
তুর তুই মাগি পাও,1,"Meme, TikTok and others"
শালির দুধ যে কতজনে হাত দিছে,1,"Meme, TikTok and others"
সেউয়ার নায়িকা,1,"Meme, TikTok and others"
শুওরের বাচ্চাএই হাতের বিচার হবে একদিন,1,"Meme, TikTok and others"
ধন্যবাদ পোশাশনকে এই কুত্তাটাকে শাস্তি দেয়ার জন্য,1,"Meme, TikTok and others"
এই রকম লোকের গলায় পা দিয়ে মারা উচিত,1,"Meme, TikTok and others"
কুত্তার বাচ্ছাকে বহিস্কার করা হোক,1,"Meme, TikTok and others"
ঐ কুততার বাচ্চা জানুয়ার এ খারাপ ছবি দিয়েছিস কেনতর মা বোনের ছবি রাখ,1,"Meme, TikTok and others"
শালার ফালতু পোস্ট,1,"Meme, TikTok and others"
বুবলির দুধ এত বড় কেন সাকিব খান টিপে টিপে বড় করে ফেলেছে না,1,"Meme, TikTok and others"
মাদারছদ,1,"Meme, TikTok and others"
মাগির পোলারে পাইলে যুতা দিয়ে মারমু,1,"Meme, TikTok and others"
এই কুত্তার বাচ্চাকে জন্ম দিয়ে ভুল করছে এই জানোয়ারটা মানুষ না কুত্তার বাচ্চা,1,"Meme, TikTok and others"
জানোয়ারের বাচ্চাতোক চুদাব পাবনার পাগল দিয়েমাদারচোদ তুমি নামাজ নিয়ে ফাল্তু কথা বল নাহ,1,"Meme, TikTok and others"
ও একটা বিয়াদফ মাদারছুদ,1,"Meme, TikTok and others"
পাগল নাকি তুই,1,"Meme, TikTok and others"
শালা তুই গাজা খাইছচ না কি সাগরের সাথে শতাংশ আর মিয়ানমারের সাথে শতাংশ,1,"Meme, TikTok and others"
এই শয়তানকে হাজার বার ফাসি দেওয়া দরকার,1,"Meme, TikTok and others"
চোদার আলাপ তো করলি না,1,"Meme, TikTok and others"
শালা বাংগালি বাটপার ৷জুতা মারার দরকার তোরে শালারপূ শালা৷ ভিডিওর শিরোনামে লেখছস কি আর দেখাইছস কি,1,"Meme, TikTok and others"
সালা তুই মানুস না তর মত ছেলে জেন দুনিয়াতে আর কারো গরে না আসে,1,"Meme, TikTok and others"
বাপ্পী অপু মুভি চুদ লাম,1,"Meme, TikTok and others"
তোর মা রাজা কার কুত্তার বাচ্চা,1,"Meme, TikTok and others"
জানোয়ার এই এডমিন নাকি অন্যকিছু কি দিয়েছে গেয়ে কাঁপালেন কোথায় একদিন হয়তো কাঁপাবেন আর কাঁপালেন এই দুটো শব্দ যে এক নয় সেটা তো এডমিন নিশ্চয়ই জানেন জেনেশুনে মিথ্যা দিয়েছেন উনি মিথ্যাবাদী অসৎ একটা অমানুষ এরাই কে ছোটো করছে কারণ যা বলা হচ্ছে এর হয়ে তাঁকে সাপোর্ট করে বলা হচ্ছে তো সেখানে যদি মিথ্যা থাকে তাহলে সেটা এর ভাবমূর্তি কেই ছোটো করে কে বড়ো হতে দিন এখনও পর্যন্ত তিনি কোনও জায়গায় পৌঁছন নি নীরবে কাজ করতে দিন নাম এমনিতেই হবে উনি যতো না পেয়েছেন তার চেয়ে বেশি ঢাক পেটানো হচ্ছে ডাক পেটানো এর সাথে সম মাত্রার না এলে কারণ এ এরকম আগেও অনেকে এসেছেন সত্যি ভালো প্রতিভা নিয়ে নি খুব বাজে ব্যাপার হয়ে যাবে,1,"Meme, TikTok and others"
টকশো চোদানোর দরকার কি চেম্বারে বসে থাকবেন যাদের বড় ছোট করার ইচ্ছা শুধু তাদেরকে সাজেশন দিবেন,1,"Meme, TikTok and others"
এতো খারাপ কি করে হয় ওর মতো সন্তান কে মাটিতে পুএে পাথর মারা উচিত,1,"Meme, TikTok and others"
সালারে ফাসি দেওয়া হুক,1,"Meme, TikTok and others"
আমি রানু গান চাই না হিমেস ভাই রানু কুকুরের পেটে কি ঘি হজম হয় শালি চাই না চাই না,1,"Meme, TikTok and others"
এই মাগি তোর বিরার ছাইজ কত লিখে পাটা,1,"Meme, TikTok and others"
নামাজ নিয়ে খারাপ মন্তব্য করবিনা ছাগল,1,"Meme, TikTok and others"
এই লোক কে মেরে ফেলা উচিত,1,"Meme, TikTok and others"
মাগির ফুয়ার বাড়ি কান,1,"Meme, TikTok and others"
সৌদি রাষ্ট্র প্রধানরা নাম্বার শুকর,1,"Meme, TikTok and others"
এই মাগীকে নাইকা বানাইছে কোন শালায়,1,"Meme, TikTok and others"
তোমার সাইজ কত সৌদি প্রবাসি,1,"Meme, TikTok and others"
ওদের কপালে জুতা মারআর যে শালি েএসব রেকর্ড করেছে সেই মনে হয একসময় পর্ন তারকা ছিলেন জুতা মারি তোর কপালে,1,"Meme, TikTok and others"
শালার মাদারচোদ,1,"Meme, TikTok and others"
বালের নায়ক,1,"Meme, TikTok and others"
এই যে মাগি তর বোধার লেট কত✈,1,"Meme, TikTok and others"
মিন্নি কি করে বুঝলো ইয়ার মেশানো পানি শয়তান নষ্ট বেয়দব খারাপ মেয়ে কে ফাঁসি,1,"Meme, TikTok and others"
ফামিূদা মিথ্যা খবর বন্ধ কর না হলে তোমার মা কে তো করবো সাতে তোমারে ও চোদবো মাগি একটা,1,"Meme, TikTok and others"
কুত্তা জারজ,1,"Meme, TikTok and others"
ফালতু খবর কেন দিসতোর বোনরে আর তোরে চুদার জন্য নাকি,1,"Meme, TikTok and others"
এই কুকুর টা কে এমন করে মেরা পেলা হোক যাতে এর মরা দেখে সরা পৃথিবীর ছেলেরা শিক্ষা পায় যাতে বাবা মা কে কোন ছেলে মারা শাহস না পায়,1,"Meme, TikTok and others"
শালা আবার বাবাকে রাখে ভাংগা ঘোরে নিজে থাকে বিল্ডিং ঘোরে,1,"Meme, TikTok and others"
এই রকম ছেলেকে পেটানো দরকার,1,"Meme, TikTok and others"
বেশ্যার আবার বিচারপতি হওয়ার ভাবনা,1,"Meme, TikTok and others"
শাকিব পাগল ছাগলের,1,"Meme, TikTok and others"
এই মাগি চোদা খাইছে অনেক,1,"Meme, TikTok and others"
হায়রে দুধরে যদি একটিবার টিপ দিতে পারতাম,1,"Meme, TikTok and others"
এই কুত্তার বাচ্চা ছেলে আর ওর বউ ওদের সন্তানের হাতে খুন হবে 🤬,1,"Meme, TikTok and others"
সব গুলাই ব্যশ্যা,1,"Meme, TikTok and others"
আবাল নায়াক,1,"Meme, TikTok and others"
এ বাচ্চার ধোন তোর মার ভোদার ভিতর দে খাঙ্কির পোলা,1,"Meme, TikTok and others"
মা বাবা বৃদ্ধ হয়ে গেলে ছেলে মেয়ে গুলা মনে হয় একটা কিছু হয়ে যায় মা বাপ কত কষ্ট করে ছেলে মেয়েকে বড় করছে সেটা ভুলেই যাই জানোয়ার কোথাকার,1,"Meme, TikTok and others"
মাগীর সংবাদ মিথ্যা,1,"Meme, TikTok and others"
ওরে কুত্তা দিয়া চুদানো দরকার,1,"Meme, TikTok and others"
সালারে আগে সবার সামনে কিছু উত্তম মাধ্যম দিয়ে তারপরে আইনের কাছে দেয়া উচিত ছিল ঐ বাবার গু খাওয়ানো ও উচিত ছিল,1,"Meme, TikTok and others"
জানোয়ার টাকে শুটিং না করে একে মেরে দেওয়া উচিত ছিলআমার মনে হচ্ছে এটা মানুষের সন্তান হতে পারে না এটা কোন জানোয়ারের সন্তান হতে পারে,1,"Meme, TikTok and others"
ওই শালী তুই লিখলে কি আর বললে কি মাগী সব ভূয়া,1,"Meme, TikTok and others"
আহ বো কা চোদা,1,"Meme, TikTok and others"
এই চানালহল খানকিমাগির,1,"Meme, TikTok and others"
নডির পুত খানকির পুলা তরে যদি পাইতাম রে,1,"Meme, TikTok and others"
খানিকির পোলা তোরে গুষ্টি চুদি মাদারচোদ নেশাখোরের বাচ্চা তোর পুটকি দিয়ে আইড্ডা বাঁশ ঢুকাবো মাদারচোদ তুই দেশে আয়,1,"Meme, TikTok and others"
মাদারচোদ যা নিজামীর সাথে পুটকি মারামারি করগা বাইঞ্চোদ,1,"Meme, TikTok and others"
এই কুতা বাডে না পালন করে এতিম গরিব অসহায় মানুষেকে টাকা গুলি দেও কাজে আসবে,1,"Meme, TikTok and others"
জানোয়ারটিকে হাত কাটা উচিত ছিলো তাহলে ও জানোয়ারটা বুঝতে পারতো বাবা কি জিনিস ও যখন বাবাকে মারছে আমার বুকের ভিতর কি করছিলো আমি নিজেই বলতে পারবো না,1,"Meme, TikTok and others"
সালা সাকিব তোরে জুতা মারার দরকার,1,"Meme, TikTok and others"
তর মার বিতর হানদায়া দিমু,1,"Meme, TikTok and others"
নরপশু নরপিশাচ বলেলও কম হবে,1,"Meme, TikTok and others"
জুতা মার জানোয়ারেরফাসি চাইযাতে কোন সন্তান এমন না করে এটা করতে সাহস না পায়কোন ক্ষমা হবেনাসাথে বউকে নিলো না কেনবউ হচ্ছে আর জানোয়ারের বাচ্চা,1,"Meme, TikTok and others"
জানোয়ারের বাচ্চা ছোটবেলায় খাওয়াইছে না বাপ মায় কুত্তার বাচ্চা খুন করার মত পোলারে,1,"Meme, TikTok and others"
সে একজন মাগী,1,"Meme, TikTok and others"
খানকির পুতের এতগুন হের মায়রে আমি চুদি,1,"Meme, TikTok and others"
সিফাত উল্লাহ দাদু যামু সুন্দরবন নিয়া আহুম হাতির ধন আইনা তর মাবইনেরে উপ্তা কইরা দিমু কঠিন এক চোদন ✌,1,"Meme, TikTok and others"
আমরা যদি এই বার ক্ষমাতা আসি হাছিনা মাগিকে চুদব,1,"Meme, TikTok and others"
মাগির বাচ্চা নামের সংগে ছবির মিল কোথায় ব্র‍্যান্ডি লাভ আভা আডামস,1,"Meme, TikTok and others"
আল্লাহ এই হারামজাদাকে হেদায়ত দান করো তারাতারি প্রিজ এরে মৃতু দান করো আমিন,1,"Meme, TikTok and others"
কানকির পুত চুপ তাক,1,"Meme, TikTok and others"
বাপ্পি সালা আবাল চুদা,1,"Meme, TikTok and others"
আরে জানোয়ার এই বাবাই তোকে খাওয়ানো শিখিয়েছে আর এই বাবার সাথে এমন করলি আল্লাহ এর বিচার করবে,1,"Meme, TikTok and others"
খানকির পুত তর মায়ের ভুদাটা আবার ভইরা দিমু তুই মুহাম্মদকে নিয়ে খারাপ কথা বলছ,1,"Meme, TikTok and others"
তোর মতন গান কি আর আছে দেশে কত সোনা আর বোদার বিতে ঢুকাইতে পারবি তোর বোদা কি যমুনা সেতুর গান হয়ে গেছে,1,"Meme, TikTok and others"
রানুকে কুকুরের মতো হাসলে লাগে ইষ্টসনেরে কুকুর ঝুটা ভাত খেয়ে বড়ো লোখ হলো,1,"Meme, TikTok and others"
সয়তান ডাঃ এই গুলি মেয়েরা মেয়েদের মধ্যে অালোচনা কর দরকার পারলে খুলে দেখা ডাঃ হারামি মেয়ে,1,"Meme, TikTok and others"
সালারে সুলে চড়ানো দরকার,1,"Meme, TikTok and others"
খানকী মাগীর চ্যানেল কোনো দিন বলেনি যে মুসলিমদের নাগরিকত্ব দেবে না যারা এই দেশীয় তাদের নাগরিকত্ব দেবে আর যারা বহিরাগত তাদের লাথি মেরে তাড়ানো হবে মানুষ কে ভুল বাল বলা বন্দ করো না হলে কেলানই খাবি চ্যানেল রিপোর্ট করলাম,1,"Meme, TikTok and others"
সালার বারী কই তার ফাসি চাই আমার তো কান্না পাচ্চে ভাই আমার বুক কাপছে ভিডিওটি দেখে ভাই কিজে করি সালাকে জদি কখনো দেখি তাহলে সালার হাত ভেংগে দিবো আমী,1,"Meme, TikTok and others"
পূর্ণিমা পুরাই সেক্সি,1,"Meme, TikTok and others"
তুই এত খাংকী লাভালো চেহেরা থাকলে কইতাম,1,"Meme, TikTok and others"
রানু পাগলিকে পাগলাগারে পাটিয়েদেন এই মহিলাকে শিল্পী গষ্টী থেকে বের করে দেয়া হওক,1,"Meme, TikTok and others"
ওতো মানুশ না জানোয়ার,1,"Meme, TikTok and others"
এই তর মাক্কে চুদি বাংলাদেশ এ আই ক বাংলা চুদা চুদব তরে,1,"Meme, TikTok and others"
ওই মা কি আমার কাছে হুগামারা দিবি তোর মালটা আমি চাটবো,1,"Meme, TikTok and others"
এই সালাকে যথাযথ সাস্তি দেওয়া হক বিশেষ করে ফাশি যারা একমত তারা লাইক দিন,1,"Meme, TikTok and others"
চৈতালি রায় মাগি তকে হালালা করবো আর অবিসি কে ভারত থেকে তারাবো,1,"Meme, TikTok and others"
ফাসি চাই জানোআরের,1,"Meme, TikTok and others"
হালাপুতের বলদ মার্কা নায়ক,1,"Meme, TikTok and others"
এই কুত্তার বাচ্চা তর মাইয়া রে বাশ ভরমুখানকির পোলা মোহা্মমদ সা কে নিয়া কথা বললে তরগুস্তির সস্তি পুজা করে দেব হারামির বাচ্চা,1,"Meme, TikTok and others"
তাইরে জন মামা দিয়ে চুদানো দরকার,1,"Meme, TikTok and others"
বুড়া জানোয়ার,1,"Meme, TikTok and others"
ও মানুষ নামে পশু,1,"Meme, TikTok and others"
আপুর আজ এমনটা হতনা আপুকে আমার ভালোলাগে,1,"Meme, TikTok and others"
এরা জারজ সন্তান,1,"Meme, TikTok and others"
হালয় বেদব নামজ কে গালি দিছে আল্লাহ তাআলা ওনা কে হেদায়েত দান করুক,1,"Meme, TikTok and others"
ওকে পুলিশে না দিয়ে গণো পিটুনি দেওয়া উচিতআমার মনে হয় এই মুরব্বি ওর বাবা না ও তো একটা জানোয়ারের বাচ্চা,1,"Meme, TikTok and others"
শালা কে ফাসির থেকেও জঘন্য শাস্তি দেওয়া দরকার,1,"Meme, TikTok and others"
খানকির পোলা সিফাত তর মেয়েরে চুদি,1,"Meme, TikTok and others"
শালারে কঠিন শাস্তি দেওয়া হক,1,"Meme, TikTok and others"
গানকির পোলা তর মাইরে চুদি ব্যবহার খারাপ করছ কেন,1,"Meme, TikTok and others"
মাদারছোদ,1,"Meme, TikTok and others"
ওরা যদি ফ্রী যৌনসুখ দেয় তুই কত টাকা দিয়ে চুদাংফা,1,"Meme, TikTok and others"
কুত্তার বাচ্চারে ফাসি দেওয়া উচিৎ,1,"Meme, TikTok and others"
শালার পো শালা তুই ছিলি ঐখানে খানকির পোলা ফালতু খবর দেওয়া বন্দ কর,1,"Meme, TikTok and others"
কু্ত্তার বাচ্চা বালের ভিডিও নি দেস,1,"Meme, TikTok and others"
জানোয়ার তুই নামাজ লই কথা বলচ,1,"Meme, TikTok and others"
কুওার বাচচা কে বিচার চায়,1,"Meme, TikTok and others"
মাগীর পোলারে জিন্দা কবর দেওয়া দরকার,1,"Meme, TikTok and others"
রানু একটা ডেমুন ম্যাগী,1,"Meme, TikTok and others"
শুয়রটারে সামনে দেখলেই পিটামুমাদারী পারলে আমার সাথে আয় হাত ভাইঙ্গা তর পাছা দিয়া ঢুকামু,1,"Meme, TikTok and others"
সাথে আপনার ব্রার সাইজ টা বললে আরো ভালো হতো,1,"Meme, TikTok and others"
মুদির মুখে মুতি,1,"Meme, TikTok and others"
তোর মাকে চুদি,1,"Meme, TikTok and others"
তোরে ঝারু দিয়া পিটামু,1,"Meme, TikTok and others"
লুচা মাদার চোদ,1,"Meme, TikTok and others"
দাদু তোমার কলিজা কত বড় তুমি নিজেও বলতে পারবে নাসব চুদো কোনো বাধা নাইকিন্তু ইসলাম নিয়ে কিছু বলিসনা তোর সোনা সাথে থাকবে নাদাদু,1,"Meme, TikTok and others"
এমন ছেলের হাত কেটে দেয় উচিত চোখে পানি চলে আসলো আল্লাহ যেন এমন কিছু আর না দেখায়,1,"Meme, TikTok and others"
ভিখারি ভিখারী হয় চাচার লজ্জা হয় আমি লাইক দিয়ে অনেক ভুল করেছি,1,"Meme, TikTok and others"
সব কিছু যেনে ভিডিও করবেন আপা নয়নের সাথে যদি বিবাহ হতো তাহলে রিফাতের বিবাহর সময় কেন বাধা দিল না তখন কোথায় ছিল এই নয়ন দেশে কি আইন নেই তখন কোথায় ছিল এই ভিলেন নয়ন কুক্তার বাচ্চা,1,"Meme, TikTok and others"
এই কুলাংার ছেলেকে বাড়ি ছাড়া করা উচিৎ ওই কুলাংেরের কি কোন সান্তান আছে ওর কপালে জেনো এটাই হবে,1,"Meme, TikTok and others"
মিননিকে চোদে পুলিশে আরাম পেয়েছে ইনচি দোন লাগবে মিননির বোদায় অনেক ধার মনে হয়,1,"Meme, TikTok and others"
খিনকির পলা,1,"Meme, TikTok and others"
তোরে কুত্তার বাচ্চা বলে গালিও দিতে পারছি না তোর মা বাবর জন্য তোরে আমি পাইলে আমার মেগাজিনের সব কটা গুলি তোর বোকে ফুটাতাম,1,"Meme, TikTok and others"
এই বাল চাল নিউজ প্রচার করার আগে একবার ভেবে দেখিস এটা ভুল না ঠিক অতিন বাবুর নামে এইসব প্রচার করিস না,1,"Meme, TikTok and others"
খানকির চেহারা দেখলেও সোনা খাড়ায়া যায়,1,"Meme, TikTok and others"
এই কুত্তা কে ফাশি দেয়া দাকার,1,"Meme, TikTok and others"
মেডাম তো নিজে টানা দিছে বুড়ার ধন তো ফাইটা যাইতাছে,1,"Meme, TikTok and others"
মাদারচোদের ঘে চাঁদা না হলে কোনো পূজা হই না শালা ভিখারির বাচ্চারা,1,"Meme, TikTok and others"
মিথুকমাগীখবরকছ,1,"Meme, TikTok and others"
এইদরনের সালিদেরকে জদী গুরা অথবা অস্টলিয়ান সার গরু অথবা বিদেশি কুত্তা দিয়ে করলে ভাল হবে,1,"Meme, TikTok and others"
মৌসুমি একটা নেচ্ছা মহিলা,1,"Meme, TikTok and others"
মাদারচোদরে পেছন দিয়ে গরম ডিম ডুকরানো উচিত,1,"Meme, TikTok and others"
হালা হলো কুত্তা,1,"Meme, TikTok and others"
এই কুত্তার বাসাটা কই ভাই,1,"Meme, TikTok and others"
কুততার বাচচা কে দরে মুরন দেওয়া দরকার,1,"Meme, TikTok and others"
বালের মাগি দুধিই নাই,1,"Meme, TikTok and others"
ওর হাত পা এবং মুখ কয়েক দিন পর অচল হয়ে যাবে ঈশ্বর এটাই যেন হয় জানোয়ার কোথাকার,1,"Meme, TikTok and others"
মাদারচদছেলে,1,"Meme, TikTok and others"
দুধ এত ছোট কেন,1,"Meme, TikTok and others"
তোৱ আমাৱ কুতাৱ মোতো লাগে,1,"Meme, TikTok and others"
মাগির পুয়া তোর বাড়ি কইতোর মারে ছুদিতোর মার হেডা কাতোর মায়ের তুই চুদ,1,"Meme, TikTok and others"
কে কে আছেন অন লাইন লাইক কমেন্ট করে সঙ্গে থাকুন ভাই যারা মিথিলাকে ঘৃণা করেন তারা লাইক দিন বাংলাদেশের পচা শামুক মিথিলাকে ভারতে পাচার করলাম এই খানকি মিথিলাকে ভারত ইন্ডিয়া কে দিয়েই বাংলাদেশে অনেক শান্তি পেল আমারা অনেক খুশি হয়েছি ভারতে পাচার করে আর কিছুদিন পর দেখব তাহার মধুরস খাইয়ে বাংলাদেশ পার করে দিয়েছে তখনই আমরা ধরে মাজায় লাথি মেরে আবার ভারতে পাচার করব যেমন আগে পার করেছি পচা শামুক নাস্তিক তসলিমা নাসরিন এবার দিলাম বেশ্যা মিথিলা,1,"Meme, TikTok and others"
তুমার চুদা দিতাম,1,"Meme, TikTok and others"
এই কুত্তার ফাসি চাই এ কেমন ধরনের বিচার হে আল্লাহ আমরা কোন দুনিয়ায বাস করি এই ছেলেকে এমন শাস্তি দেন যে আর কোন ছেলে মেয়েরা যেন করতে পারে না প্রবাসী,1,"Meme, TikTok and others"
এতো খারাব সন্তান যেন কারো না হয় খানকি মাগি দেখে দারিয়ে,1,"Meme, TikTok and others"
এই মাদারচোদের বাচ্চারা তো ফাঁসি দেওয়ার দরকার,1,"Meme, TikTok and others"
এই বেইশা মাগী তোর হেডা মিথ্যা খবর দিস কেন,1,"Meme, TikTok and others"
দা ওরে ধইরা গন চুদিতে হব্বে,1,"Meme, TikTok and others"
তোর মেয়ে কে লাগা আর মদ খা,1,"Meme, TikTok and others"
তুই সালা একটা মাদার,1,"Meme, TikTok and others"
এই মাগি চুপ তোর বালে খবর বন্ধ কর কাসমিরে ভারতের লাাখ সেনা আছে কি করে আসবে জনগি,1,"Meme, TikTok and others"
শালার পোলা খানকির পোলা তরে জুতা দিয়া বইরামু,1,"Meme, TikTok and others"
তুই এই লোকটার সন্তান না কারণ এই বুড়ো বাবা টা একজন মানুষ আর তুই হইলি শুয়োরের বাচ্চা মানুষরূপী শুয়ার দেখলাম আজ তোরে শত শত কোটিবার ফাঁসি দিলেও কম হবে কিয়ামত পর্যন্ত তোর ঐ নাপাক গালে জুতার বারি দিলেও জ্বালা মিটবে না,1,"Meme, TikTok and others"
রামের জনম ওই ছে কে জানে তা কে তেকেছ,1,"Meme, TikTok and others"
তোর মারে এনে দে চুইদা তোর মত আরো একটা জারজ বানাক,1,"Meme, TikTok and others"
এর কোনো খমাণেই পাগোল তো পাগোল ই হয়,1,"Meme, TikTok and others"
তুই টা ঠিক লাগা নাহলে গালাগালি খাবি সালি,1,"Meme, TikTok and others"
বোদা মার্কা নায়ক গুয়ামারা দিয়ে মইরা জান তাই দুয়া করি,1,"Meme, TikTok and others"
সালা তুর হাসি কই এখনহা হা হা,1,"Meme, TikTok and others"
সবথেকে বড় মিথ্যা প্রচার এই শুয়োর গুলো চ্যানেল কেন খুলে সেটাই চিন্তার বিষয়,1,"Meme, TikTok and others"
এই ভারতের হিনদূ মালাউন জদি বাবরী মসজিদে আকরোমন করো তাহলে ভিসো জূধো হবে তবে আমরা ভিসো জূধো রাজি জান দিতে রাজি তবূ বাবরী মসজিদে হাত দিলে জীবন শেষ মালাউনের বাচচারা হূসিয়ার তাকো বাচতে হলে বাবরী মসজিদে হাত দিবায় না খবর দার মালাউন,1,"Meme, TikTok and others"
খানকির ছেলে একটা শাকিব,1,"Meme, TikTok and others"
এই খানকির পোলা তরে যদি পাইতাম তাহলে খোদার কসম তরে কি করতাম আল্লায় জানে ওই কুক্তার বাচ্চা ভাই সাংবাদিক আপনি যদি বাবা মাকে ভালোবাসেন তাহলে খানকির পোলাকে আমাদের হাতে তুলে দিন ভাই আপনার আল্লার দোহায় ভাই আমি আর নিতে পারছিনা ভাই খানকির পুতে কোথায় কাজ করে,1,"Meme, TikTok and others"
শালা বুড়ো ভাঁড়,1,"Meme, TikTok and others"
আহারে সালা জানোয়ারের ফাঁসি চাই,1,"Meme, TikTok and others"
ছেলে বাবা কে মারতেছেআর এক খানকি দেখে চলে গেছেখানকি দের জন্য এই জানোয়ারের জন্ম হয়,1,"Meme, TikTok and others"
এই কুকুরের কঠিন থেকে কঠিন সাজা হওয়া উচিত সাথে ওর বৌয়ের ও সাজা হওয়া উচিত,1,"Meme, TikTok and others"
বাংলাদেশের জনতা হইলে ওরে আগে মাইরা নিত পরে কথা কইত শালা হারামীর বাচ্চা ওর জাহান্নামে ও‌ জায়গা হবে না,1,"Meme, TikTok and others"
পাগলের মাথা খারাপ,1,"Meme, TikTok and others"
তুই কোন জেলার তুই কি খালি চোদাদিয়ে বেরাস তোরে কাছে পাইলে টান দিয়া ফাইরা ফালাইতাম পাবনার মেয়েরা তোরে পাইলে তোরে মরিচ লাগাইয়া দিত ফাইজলামি শুরু করেছিস ইন্টারনেটে জেলার মেয়েরা ধরে তোকে বাঁশ ঢুকাইয়া দিব,1,"Meme, TikTok and others"
কি রে মাদার সুদ তর জন্মে র সমস্যা আছে এইটা কি পিক দিলে,1,"Meme, TikTok and others"
আরে সালারা তোরা যে বললি যে কে কতো টাকা নেই রাতে আর এখন বলছিস সিনেমা তে নেই সালা সব,1,"Meme, TikTok and others"
হারামজাদা পিটিয়ে মেরে ফেলা উচিৎ,1,"Meme, TikTok and others"
জয় একটা জানোয়ার ওর এসব নিয়েই মাতামাতি ও হাশোর নাশোর,1,"Meme, TikTok and others"
সালাকে মার মার মার,1,"Meme, TikTok and others"
সিফাত যারজ,1,"Meme, TikTok and others"
এমন জানোয়ার কে মৃতু্ দন্ড‌ দাওয়া উচিত,1,"Meme, TikTok and others"
ভারতের হিন্দুরা বেইমান ওদেরকে সাইজ করা হোক,1,"Meme, TikTok and others"
কুলাংগার ছেলের বউ কেও দরা উচিতছিলো তার বউর কথা সুনে এমন কাজ করে মাজে মাজে,1,"Meme, TikTok and others"
মদিকেএকশজুতামারী,1,"Meme, TikTok and others"
এক নম্বরের খানকির ছেলে তুই গুদমারানির ব্যাটা,1,"Meme, TikTok and others"
একে কুকুরের সাথেও তুলনা করা জায় না,1,"Meme, TikTok and others"
সালা আবাল,1,"Meme, TikTok and others"
বোকাচোদা ছেলে তোকে যে জন্ম দিল তুই তার গায়ে হাত তুলছিস,1,"Meme, TikTok and others"
শালারা ভূয়া,1,"Meme, TikTok and others"
এই রকম জালেম তো বোধ আবু জাহেল ও ছিল না,1,"Meme, TikTok and others"
খানকি মাগি বাংলাদেশে লাখ লাখ হিন্দু দের মেরে ছিস সে খবরটি প্রচার কর,1,"Meme, TikTok and others"
শুয়ারের বাচ্চাকে ফাসি দেওয়া হোকা,1,"Meme, TikTok and others"
খানকির পোলা মাগির পোলা তোর মারে চূদি মাগির পোলা তুই ইসলামের বিরুদ্ধে কথা বলিস,1,"Meme, TikTok and others"
খানকির পোলা মাগির পুতে মানুষ চেনো না হালারপুত তুই কি টপিক দিয়া ভিডিও ছাড়া দেখাশোনা কাজ পাস না খানকির পোলা তুই কি ভাবছিস আমরা এরকম ভাষায় কথা বলছি তাই ভাবছি আমরা বাঙাল কিন্তু আমরা অরজিনাল বাঙালি,1,"Meme, TikTok and others"
তোমারে কত বার চুদলে তুমি খুশি হবে ফোন দিও,1,"Meme, TikTok and others"
ওই রকম শালার জন্ম না দিয়ে যদি শুয়োর পুশতো অনেক ভালহত আমার মনেহয় শালা কুলাঙ্গার,1,"Meme, TikTok and others"
এই কুত্তার গলা থেকে শুরু করে সব অঙ্গ কেটে টুকরো টুকরো করে জালিয়ে ফেলা উচিৎ,1,"Meme, TikTok and others"
সালা জানোয়ার সেই সময় যদি আমি থাকতামগলাটা কেটে দিতাম রেসালা আর ওই খানকীর বউ টাও বেদো,1,"Meme, TikTok and others"
তুই একটা জানোআর বাবার সাতে এরকম বেবহার,1,"Meme, TikTok and others"
শালা বউ পাগলা শালাকে মারেন,1,"Meme, TikTok and others"
সিফাত কে পিডা সালা টাক্লু,1,"Meme, TikTok and others"
বেষ্যা মাগি,1,"Meme, TikTok and others"
হারামি মাগি সৌদি কি পদক্ষেপ নিলো,1,"Meme, TikTok and others"
মুদির শয়তানের ফাশি চাই,1,"Meme, TikTok and others"
তুই সুধু আমাদের বাংলার মাটিতে নাইনা হলে তোকে টুকরো টুকরো করে তোর মাংস কুকুর শিয়াল কে খাওয়া তাম🤬🤬🤬🤬,1,"Meme, TikTok and others"
চোদার খুব মজা আখিঁ মাল,1,"Meme, TikTok and others"
রেডওয়ান খা তোৃর মায়েরেরাগ বরেচুদ,1,"Meme, TikTok and others"
খানকির পলারে পাবলিকের কাছে ছেরে দেয়া হক তাতেই জন শিক্ষা পাবে,1,"Meme, TikTok and others"
দুধ এর উপর একবার হলেও যদি হাত মেরে মাল ফেলে দিতে পারতাম উঃ উঃ উঃ,1,"Meme, TikTok and others"
মাদারচোদ রে ব্রাশ ফায়ার করে মারা উচিত,1,"Meme, TikTok and others"
এই মাদারি একটা হিজড়া আগামীবার সে সেন্টার পয়েন্টে স্ট্রোক করবে তখন তার পুটকির ছিদ্র বন্ধ হয়ে যাবে এবং,1,"Meme, TikTok and others"
সরকার প্রাধানের কাছে অনুরোদ করব এই যারজ সন্তানকে ফাঁসি দেওয়া হোক,1,"Meme, TikTok and others"
ভিক্ষা করতো এইটাই ভালো ছিলো পাগল ছাগল আবার ইংলিশ বলে মানুষ ওকে দয়া করেছে আর সে কি ভাভ দেখায়,1,"Meme, TikTok and others"
সালা তুই একটা গাদা,1,"Meme, TikTok and others"
বাঙালা দেশী মাগী তোর বাঙালা দেশের নিয়ে খবর রাখ,1,"Meme, TikTok and others"
তোর গুদে কে চুদে,1,"Meme, TikTok and others"
শালা শেফুদা মাদার চুদ,1,"Meme, TikTok and others"
সালারে ফাসি দেও,1,"Meme, TikTok and others"
এই ছেলেটা জুতা মারা দরকার,1,"Meme, TikTok and others"
এই শুয়োরটাকে পিটিয়ে মেরে ফেলা দরকার,1,"Meme, TikTok and others"
হায়ওয়ানের বাচ্চা নামাজ নিয়ে গালি দিবিনা কুত্তা,1,"Meme, TikTok and others"
মাদারচোদের দর খানকির ফোলা,1,"Meme, TikTok and others"
খানকির মাগি যতো গুজব ছড়াছিস,1,"Meme, TikTok and others"
শালি রানু,1,"Meme, TikTok and others"
অামার রক্ত গরম হয়ে যাচ্ছেএমন এক দিন আসবে সেই দিন এই কুলাঙ্গার সন্তান ও বিদ্ধ বাবা হবে তখন তার সন্তান ও এমন আঘাত করবে তখন সে বুঝবে সে কত বড় ভূল করেছে যে ভূলের কোন ক্ষমা হয় না,1,"Meme, TikTok and others"
তুরে চুদার টাইম আচে,1,"Meme, TikTok and others"
আখি আলমগীর একটা বেশ্যা আর জয় একটা বেজন্মা বাস্টার্ড দুজন এক যায়গা হইছে,1,"Meme, TikTok and others"
মাগির পুত তুই নামাজকে কেন গালি দিলি,1,"Meme, TikTok and others"
এই শুয়ার টাকে ফাঁসি দেয়া হক,1,"Meme, TikTok and others"
এই জানোয়ারের দৃষ্টান্ত মূলক শাস্তি চাই,1,"Meme, TikTok and others"
ও বোকাচোদা মানুষ,1,"Meme, TikTok and others"
সালি একটা মাগি আজিজ ভাই চুদ্দা গাং কইরা দিছে,1,"Meme, TikTok and others"
এই জানোয়ারের বউ কে অন্য পুরুষ এর সাথে চুদা চদি করতে দেখে ফেলেছে তার বাবা এটাই হল আসল ঘটনা আর অন্য পুরুষ টা হলাম আমি,1,"Meme, TikTok and others"
মিন্নি একটা পতিতা,1,"Meme, TikTok and others"
তুই তর মারে চুদ খানকির পোলা,1,"Meme, TikTok and others"
ওই বাচ্চাটা ওড় ছোটো বেলাড় ছবি ওড়টা ওড়ম বড়ো হয়ে গেছিল টাই চুউদিড় বেটা এই জিনিশ পাটিয়েছে,1,"Meme, TikTok and others"
তরে আমি সামনে পাইলে খুন করতাম হারামী,1,"Meme, TikTok and others"
তুই সাহস থাকলে বাংলাদেশে আয় তুইতো পুরুষ না কাপুরষ,1,"Meme, TikTok and others"
শালার বউ ভালা না,1,"Meme, TikTok and others"
তোর লাইবে এত ভিউওজ তোর গুদ মারার জন্য,1,"Meme, TikTok and others"
পেন্টি সাইজটা ও বলে দিলে পারতেন,1,"Meme, TikTok and others"
খানকি মাগি লিখছে একটা কথা বলছে আরেকটা তোরা হচ্ছে বেসশা,1,"Meme, TikTok and others"
এই কুকুরের ফাসি চায়,1,"Meme, TikTok and others"
একটা বেব্যার কাছ থেকে এর চেয়ে ভালো কিছু আসা করা জায়না,1,"Meme, TikTok and others"
শিক্ষিত পুরুষ খোর ও মেধাবী একজন খানকি মাগী মিথিলামিথিলা কে আজীবন কোন না কোন পুরুষের রাখেন হয়ে থাকতে হবে,1,"Meme, TikTok and others"
ওর পাছা দিয়া গরম ডিম দে আর মরার আগ পর্যন্ত খুড় দিয়া গালে মুখে দাগ কাট মাদারচুদেরে,1,"Meme, TikTok and others"
তরমার ভোদাটা ভালো না,1,"Meme, TikTok and others"
এই শালীর ঘরের শালী চুদানির ঘরের চুদানি তোর মাকে চুদুম তোরে চুদুম তোর মেয়ে ও বোন কে চুদুম ভারতীয় সেনারা ভয়ে পালাচ্ছে না তোর মার হেডাত যাচ্ছে চুদতে এই শালী আর যদি টাকার জন্য এমন মিথ্যা নিউস আপলোড করিস তাহলে তুই তোর বাবার সাথে এবং তোর ভাইয়ের সাথে চুদে ব্লু ফ্লিম কর অনেক টাকা পাবি শালী তোকে ও তোর মাকে চুদবো,1,"Meme, TikTok and others"
ফাসি চাই এই নটির পুলার ফাসি চাই ফাসি চাই,1,"Meme, TikTok and others"
শালার বোকা বাঙালি এটা হল একটা গান্ডু যাকে বলে হিজরা আর হিজড়ার সাথে তোরা মজা নিচ্ছিস হাহাহাহাহা মরে গেলাম,1,"Meme, TikTok and others"
আরে ভাই তাই যদি আমাকে বলে তুমি আমাকে চুদ টাকা লাগবেনা তাকে আমি চুদমুনা মাগি,1,"Meme, TikTok and others"
পাগল লোক,1,"Meme, TikTok and others"
ধুদের ছাইজ এতো বড় কেন শালির,1,"Meme, TikTok and others"
হাসিনা মাগির প্রতিহিংসার শিকার,1,"Meme, TikTok and others"
নটি মাগি ছবি দিয়েছ কার কার আর নাম বললি কার কারমাদার চোদ,1,"Meme, TikTok and others"
কুতার বাচ্চা তোর মায়রে চুদি,1,"Meme, TikTok and others"
শালির মাগিকে পাকিস্তানের গাধাতে চুদেছে এ জন্য ভূল ভাল বকছে এটা ভারতবর্ষ হিন্দুস্তান কাউকে ভয় পেয়ে থাকে না,1,"Meme, TikTok and others"
এই খানকি মাগীটাকে ধর্ষণ করা উচিত,1,"Meme, TikTok and others"
তরে মদ খাওয়ায়ে তরে চুদামু,1,"Meme, TikTok and others"
লা নত পড়ুক মাদারের চোদের উপর,1,"Meme, TikTok and others"
এই অমানুষ টারে পাইলে জুতাপিটা করতাম অবশ্য এরে জুতাপিটা করলে জুতার অপমান হবে,1,"Meme, TikTok and others"
পুরাই আবাল,1,"Meme, TikTok and others"
মিথিলা একটা খানকি এটা নিশ্চিত হলাম তাহসানের চেয়ে ভাল ছেলে বিয়ে করে দেখায় মাগী জানি খানকি মাগী তাহসানের মতো ছেলে তোর কপালে নেই বুড়া কে বিয়া করে কি মজা পাবি বলখানকি মাগী,1,"Meme, TikTok and others"
বুবলিকে দেখলে মন চায় ওকে জুতা দিয়ে পিঠায়তে,1,"Meme, TikTok and others"
এই মাদারচোদ তে মালুখানকির পুলারে বুলি দেই মা কেন এখনো,1,"Meme, TikTok and others"
খানকির পোলা তুই বালকামা,1,"Meme, TikTok and others"
ওএকটাজানয়ার,1,"Meme, TikTok and others"
আমি বিগোতে টাইগার ফ্যামিলির সদস্য আমরা এসব পতিতাপল্লীত মাগিদের নিয়ে প্রতিবাদ করি,1,"Meme, TikTok and others"
খানকি আগেরও নষট এখনো নস্টো,1,"Meme, TikTok and others"
কি আর বলবো দুঃখের কথা এত একটা জানোয়ার তা না হলে জন্মদাতা পিতাকে কেউ এভাবে পেটায় মাকে ভালোবেসে একটা মিষ্টি খাওয়াই ছিল তাতে কি হয়েছে আর আপনারা কেন এখানে ধর্মের ভেদাভেদ করছেন কারণ আমাদের রাসূল সাল্লাল্লাহু আলাইহি ওয়াসাল্লাম তিনি আমাদের কোন ধর্মের মানুষের সাথে বেয়াদবি করার মত শিক্ষা আমাদের দেয় নি হিন্দু হোক বা খ্রিষ্টান কোন মানুষকে অসম্মান করব না সবাই মানুষ সবাই কে ভাল ভাবে দেখবা উনি তো আমার বাবার মত বিচারের মালিক আমার আল্লাহ কাকে কিভাবে কি বিচার করে আল্লাহই ভালো জানে আমাদের বলার সাধ্য নেই তাই সবাইকে বলছি ধর্ম নিয়ে কেউ বা ভেদাভেদ করবেন না আপনার ধর্ম আপনার মতই চালিয়ে যান আর আমাদের ইসলাম আমরা আমাদের মতই চালিয়ে যাব কিন্তু আমাদের আপনাদের বলার কিছু নাই,1,"Meme, TikTok and others"
শালার কুওার বাচ্চারে টুকরো টুকরো করে কাটতে হবেজানোয়ারের বাচ্চা,1,"Meme, TikTok and others"
ভাই আমাকে মাইরি ফেলা বাপ্পি নায়ক হল কি করে রেএই শালার অভিনয় দেখছিলাম একটা ছবিতে পুরা ছবি দেখছি আর হাসেছি কিন্তু কান্নার সময় আমি আরও বেশি হেসেছি,1,"Meme, TikTok and others"
আমেরিকায় কি চুদা দেয় নাকি খানকি মাগি,1,"Meme, TikTok and others"
মোদির দুই গালে জুতা মারো তাহলে পাকিস্তান জিন্দাবাদ,1,"Meme, TikTok and others"
কুত্তার বাচ্ছা মাগির পোলা তর পাছা দিয়া গরম ডিম দিয়া ফাটায় দিব,1,"Meme, TikTok and others"
নাস্তিক চুদি,1,"Meme, TikTok and others"
শালার কুত্তাটাকে পেলে গলায় পারা দিয়ে মেরে ফেলতাম শুয়োর কোথাকার,1,"Meme, TikTok and others"
সালাকে লেংটা করে মার সাথে তার স্ত্রিকেও,1,"Meme, TikTok and others"
শালী পাগলী,1,"Meme, TikTok and others"
এই কুত্তার ফাসি চাই,1,"Meme, TikTok and others"
তোর খবরের মারে চুদি এই মাগী হেড লাইনে কি লিখা তোর গুদ নাকি তোর মার গুদ তোরে কাছে পেলে চুদে পানি তোর গালে ঢালতাম,1,"Meme, TikTok and others"
দুর মাগি রাতে বেগুন ডুকাই শুয়ে থাকিস,1,"Meme, TikTok and others"
সাবিব ছাড়া অপু কুত্তায় ছাটেনা,1,"Meme, TikTok and others"
চাকরি থেকে বার করে দিন পশুটাকে,1,"Meme, TikTok and others"
শালা মোদি কে মারতে হবে ওনেক ওন্যায় করতেচে কসমির নিয়ে পরোকার পানি চেরে বাংলাদেসের খতিকরচে জাকের কে নিয়ে তালবাহানা করচে আর ও ওনেক,1,"Meme, TikTok and others"
ওর সাহস হলো কিভাবে আমাদের ভালবাসার মানুষ হজরত মুহাম্মাদ স রে গালি দিলো বেজন্মা এই খানকির পোলা রে পাইলে মদের বতোল ওর গুয়ার ভিতর দিয়ে দিতাম আমার মনে হয় ওর জন্ম মাগি পারায় বই ছে কতো জন যে ওর বাপ ও নিযেউ বলতে পারবে না,1,"Meme, TikTok and others"
বোকাচোদা তোদের কোন খেয়েদেয়ে কাজ নেই নাকি এরকম ভিডিও বানাস,1,"Meme, TikTok and others"
এগুলার সরম লজ্জা কিছুই নাই আর থাকবে কি করে যেই চেহারা কুত্তায় দেয়না পাহারাএরা ফিল্ম ইন্ডাষ্ট্রিতে আসে পরিচালকের সাথে রাত কাটিয়ে তাহলে সরম থাকেনি একশ টা কুত্তা দিয়া চুদানোর দরকারমাগিরে,1,"Meme, TikTok and others"
তুরানিজেই জানিসনা তোদের দেবতা আসলনানকল আমরা এই বিচার মানিনা আমার আললার জমিনে থেকে আললাকে ভিখা দেয় কোন কুকুরের বাচচা জজ আমি একটা মেয়ে তবু বলছি দেখেনেব কুকুরের বাচচা মদিকে আরজজকে,1,"Meme, TikTok and others"
ঐ একটা জারজ সন্তান,1,"Meme, TikTok and others"
বাইনচোদের বাচ্ছা নামাজ নিয়া বাজে কথা বলবি না সালা হিন্দুর বাচ্ছা,1,"Meme, TikTok and others"
ভাই আপনারা তাকে দশ বছর জেল দেন আর জদি না দেন তা হলে তার বাবার বয়ষী এই লোক টাকে মেরে পেলবে এই জানোয়ার টা,1,"Meme, TikTok and others"
খানকিমাগি এইসব বালছাল খবর কোথা থেকে জোগাড় করিস,1,"Meme, TikTok and others"
তুই এমেরিকা কোন জায়গায় তাকিস তরে জবাই করবো বল,1,"Meme, TikTok and others"
তর মারে চুদ,1,"Meme, TikTok and others"
ওই কুকুর কে প্রক্যাশে ফাঁসি দেওয়া দরকার শুনছেন বাংলাদেশ সরকার,1,"Meme, TikTok and others"
কি বলিশ রে খাংকির পো আমার দেশ নিয়ে আমার জাতি নিয়ে কথা বলিশতোর মাকে চুদে ভোদা ফাটিয়ে দিবো রে না স্তিকের পোমদ নারে তুই আমার চেটের মাল খা চুদির ভাইমাঘির পোলা,1,"Meme, TikTok and others"
বানচদের বাড়ি কোথায় সালারে সামনে পাইলে এইরম মার মারলাম অইলেসালার পুতে বাবার গায়ে হাত তুলছে,1,"Meme, TikTok and others"
তোর শাওয়ার ভিতরে বাঁশ দেওয়া দরকার,1,"Meme, TikTok and others"
মোদির সাথে তসলিমা নাসরীন কে নিকাহ দেওয়া হোকগো মূত্র পান করান,1,"Meme, TikTok and others"
খানকি মাগিতোকে বার বার বারন কোরেছি এসব মিথ্যা খবর গুলি প্রচার কোরবি না এর পরেও যদি না সুনবি তাহলে তোর মুখে বাড়া ঢুকিয়ে দেব,1,"Meme, TikTok and others"
এরকম ছেলেকে চৌমাথা রাস্তার মোড়ে নগ্ন করে গনধোলাই দেওয়া উচিৎ,1,"Meme, TikTok and others"
দূর শালা,1,"Meme, TikTok and others"
মাদারচোদ কে গুলি করে মারা দরকার,1,"Meme, TikTok and others"
এই কুত্তার বাচ্চাকে জবাই করা উচিত যারা একমত লাইক দিন,1,"Meme, TikTok and others"
ছেলে টার ফাসি হোক চুদির ভাইকে পেলে পিটিয়ে মারতাম,1,"Meme, TikTok and others"
নায়ক না একটা রাম ছাগল,1,"Meme, TikTok and others"
কাংলাদেশী শুয়োরের বাচ্চাদের ভুল ভাল নিউজ কোথা থেকে পায় কদিন পর চীনের রাষ্ট্রপতি শি জিনপিং ভারত সফরে আসছে ছাগল তোরা দেখবি আর জ্বলবি,1,"Meme, TikTok and others"
জানোয়ারের কঠোর শাস্তি চাই,1,"Meme, TikTok and others"
তোর জদি বড় করার ইছে থাকে তহলে তুই বলতি আমরা জ চিলাম টিপে বড়রো করে দিতাম,1,"Meme, TikTok and others"
কুত্তা মাগির পোলাতোর মা রে হাতি দিয়ে চোদা দরকার ছিল তা হলে তোর মার ভোদা বড় হত আর তোর মত বেশিবেশি জারজ বের হত,1,"Meme, TikTok and others"
ওতো বেশ‍্যা,1,"Meme, TikTok and others"
তর জন্ম কোনো পতিতালয়ের কনডম দুর ঘটনাই হয়েছে তুই তাই বুজাতে চাচ্ছি পতিতা লয়ের মাগি তুই,1,"Meme, TikTok and others"
এই মাগির দুধ কুততাই খাবে,1,"Meme, TikTok and others"
জানোয়ারের বাচ্চাযতোরে জন্ম দিয়েছে তুই তার গায়ে হাত তুললিতুই তো কুত্তার চেয়েও অধমতর উপরে গজব পড়বে,1,"Meme, TikTok and others"
পাগিল রানূ,1,"Meme, TikTok and others"
তিনি তার স্তনযুগলের সাথে বৈষম্য তৈরি করছেন কেনো একটিকে ওড়না দিয়ে লুকিয়ে রেখেছেন ও অন্যটিকে প্রদর্শন করছেন এটাকি বৈষম্য নয় সম অধিকার চাই স্তনের সাথেও অবিচার করা হচ্ছে,1,"Meme, TikTok and others"
নাস্তিক কুত্তার বাচ্চা,1,"Meme, TikTok and others"
হারামজাদা রে কাবাব বানানো দরকার,1,"Meme, TikTok and others"
আমি ত জয় বাবাকে ভালো বাসি আর শাকিব কুত্তা তুই বুবলিকে গিয়েচুদ,1,"Meme, TikTok and others"
আল্লাহ এই জানোয়ারের বাচ্চা কি ওরে শুয়ারের বাচ্চা,1,"Meme, TikTok and others"
মায়রে বাপ মাগির দুধ তো সেই,1,"Meme, TikTok and others"
এই খানকির পোলা শিরোনাম কি আর দেখাইলি কি,1,"Meme, TikTok and others"
ও মাগি তই একটা মাগি তোর মা ও কি মাগি চিলো,1,"Meme, TikTok and others"
বুবলি একটা খানকি,1,"Meme, TikTok and others"
তোর মায়রে ধোন দিয়া চোদাব মরা থাকলে দিয়া,1,"Meme, TikTok and others"
চুতমারানি রা,1,"Meme, TikTok and others"
মাদারচোদ টাকার জন্য ভূয়া ভিডিও তৈরি করা বন্ধ কর,1,"Meme, TikTok and others"
আপনি যে ভাষাগুলো বলেন সেই ভাষা থেকে বুঝা যায় আপনি একজন জারজ সন্তান,1,"Meme, TikTok and others"
মানুষ নামে জানোয়ার,1,"Meme, TikTok and others"
কুলাঙ্গার সন্তান আল্লাহ এই কুত্তার মৃত্যু যেন কুত্তার মতই হয়,1,"Meme, TikTok and others"
এরা সব জারজ,1,"Meme, TikTok and others"
ভাবির দু্ধের সাইজ ঠিক আছে,1,"Meme, TikTok and others"
এই কুত্তারে সামনে পাইলে আল্লার কছম আমি চামচা ছিল্লা লবন দিতাম ওর জীবন ধ্বংস হউক এটাই প্রার্থমা করি,1,"Meme, TikTok and others"
হালারে ফাসি দেওয়া উচিত,1,"Meme, TikTok and others"
সালার ত কোনো ছবি দেখি নাসালা আবাল,1,"Meme, TikTok and others"
মাদার চোদ্দ তর মা#,1,"Meme, TikTok and others"
এদেরকে জিন্দা পুড়া উচিৎত,1,"Meme, TikTok and others"
এইধরনের মাগির ফাঁশি চাই,1,"Meme, TikTok and others"
ইন্ডিয়ান নিজেরা ত পাগল সালা দুনিয়ার সবাইকে পাগল মনে করে বাবর এর কাছে জমির অভাব ছিল তাই মন্দির এর উপর মসজিদ করেছেন পাগলের কথা সব এই সব যুক্তি মিথ্যে,1,"Meme, TikTok and others"
এসব মাদারচুদের পাছায় গরম ডিম ডুকাইয়া দেওয়া দরকার,1,"Meme, TikTok and others"
সালারে মাইরা ফেলে,1,"Meme, TikTok and others"
এই মাগি তুরে চুদমো,1,"Meme, TikTok and others"
ঐ সালারে একড়া ওলা বাঁশ দাও,1,"Meme, TikTok and others"
ঐ শালা বুইড়া শয়তান একটা নাস্তিক,1,"Meme, TikTok and others"
ওই কিসের একটা চড় রে কুওার আাচ্চা তুই কয়টা চড় মারছস,1,"Meme, TikTok and others"
চোদাচো দি,1,"Meme, TikTok and others"
সালা কুত্তার বাচ্চা সেফু তুই নামাজ ও ইসলাম নিয়ে কিছু বলবি না বল্লে তোর গোষ্ঠী কুত্তা দিয়ে চোদামুসালা মাতালপাগল,1,"Meme, TikTok and others"
হেডা যদি নদী হয়ে যা কোন সমস্যা নাই,1,"Meme, TikTok and others"
জানোয়ারে বাচ্চা কে ফাসি দেওয়া হোক,1,"Meme, TikTok and others"
তুমি ঢাকাই খানকী,1,"Meme, TikTok and others"
তরে কি পাগোলে চুদি,1,"Meme, TikTok and others"
তোর মোখের মধ্যে পায়খানা দিব জালিম,1,"Meme, TikTok and others"
শুয়োর রে জান্ত আগুনে পুড়ে মাড়া উচিত,1,"Meme, TikTok and others"
জানোয়ারটাকে সামনে পাইলে জুতা পিটা করতাম,1,"Meme, TikTok and others"
ঐখানকিঐ,1,"Meme, TikTok and others"
এই খানকির পোলা পুলিশ মাদার চোদ কুকুরের বাচচা পুলিশকে ফাঁশি চাই,1,"Meme, TikTok and others"
খানকির পোলা তোর মাগি কই,1,"Meme, TikTok and others"
এই কুকুরে বাচ্চা কে আমার হাতে তুলে দিন,1,"Meme, TikTok and others"
ওকে গালি দিতেও পারছি না কুত্তার বাচ্চা শুয়ারের বাচ্চা যেটাই বলি সেটা একজন বাবাকেও আঘাত করে এইটুকু বলবো এমন ছেলেকে জনতার সন্মুখে জবাই করা হউক আমি কাছে পাইলে লুকিয়ে কোরবানি করে দিতাম শালাকে শিরচ্ছেদ করে করা হউক,1,"Meme, TikTok and others"
যে নিউজ পরছে সেটা হলো ছাগলের নাম্বার বাচ্চা পাহল কোথা কার,1,"Meme, TikTok and others"
শালা আবাল অপু বিশ্বাস দালাল,1,"Meme, TikTok and others"
খানকিমাগিআজেবাজেভিডিও বানিয়ে মানুষের বিপদকরছো,1,"Meme, TikTok and others"
কলকাতার সেক্সি মহিলা বা বিধবা বয়স্কা মহিলা থাকলে এসওওও আমার বয়স্কা দের চুদতে দারুন লাগে এ এসওওওও ভিডিও কল করে চুদবো এসওওওও,1,"Meme, TikTok and others"
নিচ তলা ভাড়া দিয়া মানে এই বুঝতাছি যে সানাইয়ের নাভির নিচের চার ইঞ্চি নৌকার মত সাগর কে মাসের জন্য রাত্রিতে ভাড়া দিয়ে নাভির উপরের ছোট আপেল কে বড় ডাব বানিয়েছে এটাই ত কি না বুঝিয়ে বলবেন,1,"Meme, TikTok and others"
মাগি তর পুটকি মারমু সাউয়ার বেটি ভুয়া খবর বলিস,1,"Meme, TikTok and others"
ওই বাহান চোদের ঠিকানাটা কি খানকির পোলা তুই একদিন এই দিন ফিরে পাবি,1,"Meme, TikTok and others"
এই কুকুরের মারাক্তক বিচার চাই,1,"Meme, TikTok and others"
কম হলে জন চুদিছে আখিকে,1,"Meme, TikTok and others"
তাই একটা মাগি,1,"Meme, TikTok and others"
মাদারদ তোরে পাইলে রাস্তায় জনগণের সামনে কুত্তার মতো পেঠাইতাম যেই বাবা তোরে এত বড় করেছে ওনার গায়ে হাত তুলতে লজ্জা লাগেনি নরকে ঠায় পাবি না তুই তোর বাবার গায়ে হাত দিসনি তোর সৃষ্টিকর্তার উপর হাত তুলেছিল আহ্ ভিডিওতে বৃদ্ধ বাবা ছেলের বিরুদ্ধে একটা কথা বলল না বাবার ভালবাসা কি জিনিস এত বছরে একদিন হলেও বাবা নিজের খাবারটুকু তোরে খাওয়াছে এটা সাতখুনের চাইতেও বড় পাপ কঠোর শাস্তি দেওয়া হোক,1,"Meme, TikTok and others"
মাগির অ্যাক্রেদিটেশন ইঞ্চি বানাইতাম,1,"Meme, TikTok and others"
এই সালাকে কঠিন শাস্তি দেওয়া হোক,1,"Meme, TikTok and others"
সানাই লাখ টাকা খরচ করে ভুল করছো দেখো টাকা ছাড়াও তোমার চেয়েও এগিয়ে মাগি এখন কুত্তা চুদে না,1,"Meme, TikTok and others"
সাকিবকে জুজা মারা দরকার লুচ্চা,1,"Meme, TikTok and others"
কুত্তার বাচ্চারা ঝাড়ু দিয়ে পিঠা হারামজাদারে,1,"Meme, TikTok and others"
বাংলাদেশের পুলিশ সালারা সবচোর,1,"Meme, TikTok and others"
কুত্তা ইন্ডিয়ান,1,"Meme, TikTok and others"
এই সব গুদ মারোনো দের কোপানো দরকার,1,"Meme, TikTok and others"
তর চৌদ্দ গুষ্টি ফকিন্নি ছিল নাস্তিকের বাচ্চা আমার নবীকে নিয়ে উল্টাপাল্টা বলবিনা,1,"Meme, TikTok and others"
এই মাগী তুই মরলে তর জানাজা পড়বে কে হুজুর কে নিয়ে যে খারাপ কথা বলছ,1,"Meme, TikTok and others"
কুত্তার বাচ্চার বাসা কই,1,"Meme, TikTok and others"
বেশশা মাগির পোলা৷ তোর পুটকিতে বাশ দিমু,1,"Meme, TikTok and others"
জাহান্নামে পুরবি তর মাফ নাই আল্লাহ তুমি বিচার করবাছি জারোচ ছেলে,1,"Meme, TikTok and others"
চুতমারানি এরা পর্ন তারকা নিজেও মনে হয় তাই তুই,1,"Meme, TikTok and others"
তোদের মত আবাল মার্কা ইউটুবারদের জন্যই এরা সেলিবেটি হচ্ছে,1,"Meme, TikTok and others"
তোমাগেরভুদায়কত্তোওরষ,1,"Meme, TikTok and others"
মাদার চোদকে ফাশি দাও,1,"Meme, TikTok and others"
মানুষ নামের জানুয়ার,1,"Meme, TikTok and others"
এই কুত্তার বচ্চা নামাজ নিয়া গালি দিলি কে,1,"Meme, TikTok and others"
এতদিন ছিল মা পাগল আর এখন হয়েছে মেয়ে ছাগল,1,"Meme, TikTok and others"
জানোয়ার ছেলেকে কেউ বোঝাতে পারছেনা যে যাকে মারছে তার জন‍্যই একদিন এই প্রথিবীর আলো দেখেছে,1,"Meme, TikTok and others"
ময়ূরী দুধ সবচেয়ে বড়,1,"Meme, TikTok and others"
মদি কুত্তা পিটাপিটা মু,1,"Meme, TikTok and others"
এই মেয়েটা খানকি ওরে কুকুর দিয়ে চুদা দরকার,1,"Meme, TikTok and others"
তুই একটা কুলাঙ্গার সন্তান,1,"Meme, TikTok and others"
সালার পাসি চাই,1,"Meme, TikTok and others"
সালি তুমি এই খবর পাইসতরে করা লাগবে,1,"Meme, TikTok and others"
খানকির ছেলে জুতো দিয়ে মেরে তোর মুখ ছিড়ে ফেলবো নিজের বাবাকে ওরকম করে কেউ মারে ওর থেকে ওর চাকরি কেড়ে নেওয়া হোক,1,"Meme, TikTok and others"
এই জানোয়ার টাকে যদি কাছে পেতাম কয়েকটা লাথি মেরে নিতাম জানোয়ারটার হাতটা কেটে নেওয়া দরকার,1,"Meme, TikTok and others"
শালা একটা অমানুষ দোয়া করি ওর জেন সন্তান একদিন জুতা পিঠা করে,1,"Meme, TikTok and others"
তরে কেউ চোদেনা,1,"Meme, TikTok and others"
এই হালারেএকটা কঠিন বাশ দেওয়া দরকার,1,"Meme, TikTok and others"
তুই যদি ইন্ডিয়ান হতিস তো এতো দিন তোর আগুনে পুড়িয়ে হত্যা করতুম,1,"Meme, TikTok and others"
এই কুত্তাকে ধরে গণধোলাই দেওয়া উচিত জানোয়ারটা যেই হাত দিয়ে মারছে সেই হাতটা ভেঙ্গে দিন,1,"Meme, TikTok and others"
মাগিপুলারে ফাসি দেওয়াহক,1,"Meme, TikTok and others"
আমি চাই মুসলিমরা জয় হোক,1,"Meme, TikTok and others"
সুয়োরটা বাবাকে কিরোম মারলো,1,"Meme, TikTok and others"
খানকির বাচ্চাকাছে পাইলে ছুলে ফেলতাম,1,"Meme, TikTok and others"
ওই মাদার চুদ তুই পারলে বাংলাদেশে এসে এগুলো বল তর লিঙ্গ কেটে কুত্তা দিয়ে খাওয়ামু বাইনচুদ বাস্টার্ডের বাচ্চা,1,"Meme, TikTok and others"
মোদি একটা শুয়োরের বাচ্চা,1,"Meme, TikTok and others"
এটার একটা কঠিন বিচার হোক ওই পশুটার বিচার চাই,1,"Meme, TikTok and others"
অপু মরলে আরো খুশি আমরা,1,"Meme, TikTok and others"
খাংকির পোলা তুই যাই বল নমাজ নিয়ে কথা বলবি না,1,"Meme, TikTok and others"
তুই একটা মাগীর দালাল,1,"Meme, TikTok and others"
এই শালাকে জুতা দিয়ে মারা উচিত,1,"Meme, TikTok and others"
আমার মনে হয় এই মাগির আর নাটকটির পুলা ব্রার গার্মেন্স আছে তার জন্যয় এরকম একটা প্রোগ্রাম করেছেন আমি ধিক্কার জানাই একুশে টেলিভিশন চ্যানেল কে ছি ছি ছি,1,"Meme, TikTok and others"
এমনিতেই তো সুন্দরতোমার ওরনা দেওয়ার দরকার ছিলো নাদিয়েছোই যখন আর একটু বড়ো করে দিলে কি হতো,1,"Meme, TikTok and others"
তুই নামাজ নিয়ে খারাপ কথা বললি কেনতোকে সামনে পাইলে এক কোপে তোর শিরউচ্ছেদ করতাম,1,"Meme, TikTok and others"
ছেলের বৌ টাও দারিয়ে দেখলো তাকে জিজ্ঞেস করলো না কেনমানুষ জানোয়ার হয়ে গেছে ছি ছি ছি,1,"Meme, TikTok and others"
গুষ্টি চুদ সালার,1,"Meme, TikTok and others"
আসলে ভারতের প্রত্যেকটা মানুষ গরু,1,"Meme, TikTok and others"
এই খানকির পোলা রে ছেড়া জুতার মালা পরিয়ে দেন আর বউয়ের আর টুকু কইলাম না,1,"Meme, TikTok and others"
সালায় একটা ছোট লোক,1,"Meme, TikTok and others"
তর মারে সুদি সালা মাদার সুদ,1,"Meme, TikTok and others"
বানচোদ হেডিং টা পাল্টা পলাতক মানে টা কি বোকাচোদা বুঝে কথা বল,1,"Meme, TikTok and others"
এই জানোয়ার যেমন ওর বাবার গায়ে হাত তুলেছে ভবিষ্যতে ওপর ছেলেও ওর গয়ে হাত তুলবে ও মানুষ না জানোয়ারের ছেয়েও অধম,1,"Meme, TikTok and others"
এই খানকির পোলার ফাশি চাই,1,"Meme, TikTok and others"
বেস্যা তাসলিমা নাসরিন কে হত্যা করে কুত্তা দিয়া খাওয়া,1,"Meme, TikTok and others"
ক্ষমা ক্ষমা শালার কোনো ক্ষমা নেই,1,"Meme, TikTok and others"
তুই জালিয়াত মাদারচোদ সাহস থাকলে দেশে আয় চোতমারানির পোলা তোর ধন কাইটা তোর মা খালেদারে খাওয়ামু মাদারচোদ,1,"Meme, TikTok and others"
এই রকম ছেলেকে পুড়িয়ে মারা উচিত,1,"Meme, TikTok and others"
শালা মদ বেশী খায়ইছে,1,"Meme, TikTok and others"
রেশমির বোদার ভিতরে গরম ডিম ঢুকায়,1,"Meme, TikTok and others"
শুয়োর সালারে পিটিয়ে মেরে ফেলা হোক,1,"Meme, TikTok and others"
এরে জবাই করে দে কেউ,1,"Meme, TikTok and others"
তুই আমার বাল জান্তিস,1,"Meme, TikTok and others"
মাদারচোদের বাচ্চা,1,"Meme, TikTok and others"
চোখের পানি আটকাতে পারলাম না ধিক্কার জানাই তোর মতো কুলাঙ্গারকে তুই পৃথিবীর সমস্ত বাবাকেই অপমানিত করলি আল্লাহ্পাক তোর জন্য উপযুক্ত শাস্তি গুছিয়ে রেখেছেন,1,"Meme, TikTok and others"
কাকা আপনার চোদা কেউ গাভিন হচ্ছে না কেন,1,"Meme, TikTok and others"
মাদার চুদ আমিতরে চুদুম,1,"Meme, TikTok and others"
মাগী তুই ওষুধের নামটা বললি না কেন বালের ভিডিও বানাস তোর মুখে আমার খাড়া ধোন দিয়ে ইচ্ছা মত্যো ঠাপ দিলাম আর আমার বীর্য তোর গলার ভেতর ফেললাম খা আমার মেডিসিন আর ভিডিও বানা,1,"Meme, TikTok and others"
সালা কে ফাঁসি দাও,1,"Meme, TikTok and others"
মিথিলা হলো মাগি এক সোনা হবে না,1,"Meme, TikTok and others"
আপু তোমার দাদুরে আমার খুব পছন্দ ইচছে করে একবার পুটকি মারতে তোমার দাদুরে যদি না পাই তাহলে তুমি আমাকে একবার পুটকি মারতে দিয়ো,1,"Meme, TikTok and others"
মাগির পোলা কসাইয়ের চেয়েও খারাপ,1,"Meme, TikTok and others"
তোর মার ব্রা সাইজ কত খানকি মাগি,1,"Meme, TikTok and others"
মোদি একটা কুত্তার বাচ্ছা,1,"Meme, TikTok and others"
মুসলিম মাদার চদ তোরা বাইরের মাল,1,"Meme, TikTok and others"
তোমার টা কতহাত দিয়া ক্রিকেট খেলা যাইবো নাকি পা দিয়া ফুটবল খেলতে হইবো,1,"Meme, TikTok and others"
ফরহমিনা তোর কথা শুনলে আমার কেমন সোনাটা সোজা হয়ে যায়,1,"Meme, TikTok and others"
নোয়াখাইল্লা কি তোর মারে পোনদাইছে নি তোর মারে তোর কুত্তা দি ছোদামু নোয়াখাইল্লা রা তোরে পোনদাই তোর পেটে বাচ্চা ওয়াই দিবো ইসলাম ধর্ম সম্পর্কে নামাজ নিয়াতুই কেন কথাবলিস হালা,1,"Meme, TikTok and others"
জানোয়ার এক কথায়এই রকম ছেলে থাকা থেকে না থাকাই ভালোবাবা কে কেউ এই রকম মারে আল্লাহ হেদায়েত দান করো,1,"Meme, TikTok and others"
মদিকেজুতামারাহক,1,"Meme, TikTok and others"
কলকাতা পুলিশ ভাইয়ের কাছে একটাই অনুরোধ ওই শালা কে যাবত জীবন কারাদণ্ড দেন,1,"Meme, TikTok and others"
এই সালারে আমার হাতে ছেড়ে দে ওরে পিসে দিবো,1,"Meme, TikTok and others"
এই কুলাগ্নারকে গুলি করে মারা উচিত,1,"Meme, TikTok and others"
বুকে ওড়না দাও নামাজ পড়ো আল্লাহর কাছে মাফ চাও বেহায়া নারী বড় বড় দুধ দেখায় পোলাপান গো,1,"Meme, TikTok and others"
সানাই মাগি টাকা দিয়ে বানাইছে এ তার চাইতে এ টাইতো সুন্দর,1,"Meme, TikTok and others"
তোর মার ভোধা,1,"Meme, TikTok and others"
ওর বারি কোথায় শালার বেটা কে চুদে মেরে ফেলা উচিত বাবা কে মারছে,1,"Meme, TikTok and others"
এই সব জানোয়ারদের সমাজের সামনে তুলে ধরা উচিত যাতে এদের দৃষ্টান্ত মূলক শাস্তি হয়,1,"Meme, TikTok and others"
আমি তোর জামাই হতে চাই তুই কি রাজি আছিস,1,"Meme, TikTok and others"
এই গানখির পোলা তুর বাড়ি কই তোরে পাইলে তুর মার বোদা দিয়া তোরে বোরা দিতাম আর তুর মারে কজনে চোইদা তুরে জরম্ম দিচেরে ওই গানগির পোলা,1,"Meme, TikTok and others"
ও রানু ভিখারী আবার কি চলছে মাথার ভিতর এরা তো বলছে তুমি নাকি খমা চেয়েছো কখন কোথায় কি ভাবে তুমি পাগল নাকি এরা পাগল আর দাদার মাথায় ফের ভুত কামরেছে সবাই দাদা কে নিয়ে অনেক কিছু লিখছেতো তাই দাদা ফের রানুর কাছে সাহায্য করতে এল এই সব নেকামো আর ভালো লাগে না ভারিতো ভালো গান করে এক দুই লাইন তার জন্যে এতকিছু,1,"Meme, TikTok and others"
এই মাদার চোদরে পাইলে জুতা দিয়ে মারতাম,1,"Meme, TikTok and others"
ভিডিও পোষ্টকারি বাইঞ্চোদ,1,"Meme, TikTok and others"
তরে চুতলে খুব মজা পাইবো খানকি ময়ে,1,"Meme, TikTok and others"
এমন ছেলেকে গায়ে আগুন দিয়ে মারা উচিত,1,"Meme, TikTok and others"
সালার কি কমু,1,"Meme, TikTok and others"
শালা পাঠা হিরো আলমের থেকেও খারাপ অভিনয় করে অথচ কথায় বড় বড় গল্প বাইনচুদের বাচ্চা,1,"Meme, TikTok and others"
ওই খানকির বাচ্চা রেন্ডির ছেলে মেয়ে মানুষকে সন্মান করতে শেখনতুন নতুন বালের ভিডিও আপলোড করিস তুই যে মেয়েটির ছবি দিয়েছিস সে কারো বোনস্ত্রী মাবোকা চোদা তোর মা বোন স্ত্রী এদের মাং এর ফুটো দুধের ছবি এগুলো,1,"Meme, TikTok and others"
মাগির পুলা তরে পাইলে তর পুটকি দিয়া,1,"Meme, TikTok and others"
এই লোকটার গায়ের চামড়া ছিলে লবন লাগিয়ে দিয়ে কড়া রোদে দাড়িয়ে রাখতে হবে যাতে যেন আর কেউ কোনদিন পিতা মাতার গায়ে হাত না তোলে,1,"Meme, TikTok and others"
মাগীর পুলাই প্রশ্ন করে আরেক মাগী#,1,"Meme, TikTok and others"
খাংকি মাগি তোর গোয়ায় কি ভারত হোল ডুগিয়েছে,1,"Meme, TikTok and others"
শালার সোনার মাথা কাটল,1,"Meme, TikTok and others"
কুত্তার বাচ্চা মানুষ না,1,"Meme, TikTok and others"
খানকির পোলা ও এমন পোলা জন্ম দেয়ায় ভুল,1,"Meme, TikTok and others"
মত খাও আর মাগি চুদেন,1,"Meme, TikTok and others"
ঐ লোকটাকে কেও আমার সামনে এনে দাও যে এনে দেবেন তার প্রতি চির জীবন কৃতজ্ঞ থাকবো প্লিজ ঐ একই টেকনিকে চুতিয়া কে ফাটাতে চাই,1,"Meme, TikTok and others"
সালা টোকে সামনে পেলে জুতা দিয়ে মারতাম সাকিবের মত নায়ক আগামী বছরেও পাবিনা,1,"Meme, TikTok and others"
ঐ মালু শুয়োরের বাচ্চাকে ফাসি দেন ফাসি,1,"Meme, TikTok and others"
তোমার টা কতো সাইজ,1,"Meme, TikTok and others"
খানকি ব্যাটা তোরো দিন আসবে,1,"Meme, TikTok and others"
তকে জদি ত্রকটা রাতের লাগি পাইতাম দেকতে তকে কিবাবে ইংলিস চুদা দিতাম,1,"Meme, TikTok and others"
সাকিব এক নাম্বার হারামি মধ্যে,1,"Meme, TikTok and others"
এমন কুলাঙ্গার ছেলে বেচে থাকার চেয়ে না থাকায় শ্রেয়,1,"Meme, TikTok and others"
কুলাংগার ছেলে,1,"Meme, TikTok and others"
এইটা কে গুলি করে মারা উচিৎ,1,"Meme, TikTok and others"
আহ্ মনুষ্যত্ব মনে রাখিস জানোয়ার তুইও একদিন বুড়ো হবি তখন তুই তোর পায়খানা খেয়ে বাঁচবি কখনোই তুই সুখ পাবিনা জানোয়ার,1,"Meme, TikTok and others"
কিরে মাগির পোলা নবীকে নিয়া গালি না দিলে তোর বাবাড়া ইউরোপের ভিসা দেয় না মাগির পোলা নবীকে নিয়া কিছু বলবি না বহুদিন ধরে কুত্তা দিয়া বুইড়া চুদাইনা,1,"Meme, TikTok and others"
তুই একটা ছাগল,1,"Meme, TikTok and others"
কুকুর শালা,1,"Meme, TikTok and others"
সালা লুচ্চা বেদব,1,"Meme, TikTok and others"
দুধ গুলো ভালোই বড় হয়েছে,1,"Meme, TikTok and others"
জবায দেরে কুত্তাকে,1,"Meme, TikTok and others"
এই দেশের কিছু খানকির পোলারা বিদেশ গিয়ে কি যে ভাব লয় মনে হয় যে কি আবার কিন্তু দেশে আসলে এদের কে কুকুর ও জিগায় না,1,"Meme, TikTok and others"
এই কুলাংগার এখোন বাঁইচা আছে,1,"Meme, TikTok and others"
এরোকম খানকির পোলাগো মাইরা হালানোর দরকার,1,"Meme, TikTok and others"
পতিতা নায়িকা,1,"Meme, TikTok and others"
তর মারে চুদি,1,"Meme, TikTok and others"
এভাবে উলঙ্গ হয়ে চলাফেরা করা হারাম ইসলামে জায়েজ নাই যদি তুমি মুসলিম অবশ্য তুমি পর্দা করবে,1,"Meme, TikTok and others"
এই মাগিরা তো দের আর কোন কাজ নেই,1,"Meme, TikTok and others"
বুবলি একটা মাগি বিয়ে ত হয়নাই শাকিবের সাথে মা হবে কি ভাবে,1,"Meme, TikTok and others"
সালা মানুষের বাচ্চা না সালা সুয়ের বাচ্চা,1,"Meme, TikTok and others"
হারামজাদা‌কে জবো করা উ‌চিৎ,1,"Meme, TikTok and others"
শালা ভন্ড,1,"Meme, TikTok and others"
শালা মোদি মালু ভারতের মুসলমানদের মেরে ফেলছেশালা বলছে তার অভ্যন্তরীণ বিষয় শালার সমালোচনা করবেনা শালাকে চুমে দিবে শালাকে ধংস করে দাও,1,"Meme, TikTok and others"
এডমিন মাগির ভোদার সাইজ কত,1,"Meme, TikTok and others"
এই সকল আবাল চাবাল যখন থেকে চলচিত্রে এসেছে তখনই বাংলার সিনেমা যগতের কপাল পুড়েছে সালা হিজড়া,1,"Meme, TikTok and others"
গরুর ফুয়া,1,"Meme, TikTok and others"
এই মাগিক চোদা চোদা হোক আর একে রিপোর্ট করা হোক সাথে আনসাস্ক্রাইভ করা হোক,1,"Meme, TikTok and others"
ঐ শুয়োরের বাচ্চার ফাসি চাই,1,"Meme, TikTok and others"
রানুর মেয়ে জুতা দিয়ে পিটানো হক সালি একটা খানকি,1,"Meme, TikTok and others"
সালা এডমিন তোর এগুলো ছাড়া কি দরকার সবাই তো বকা দিতেছে এর ভিডিও না ছাড়লে ভালো হবে,1,"Meme, TikTok and others"
হালা একটা লুচ্চা,1,"Meme, TikTok and others"
এটা কোথাকার খানকীরছেলে,1,"Meme, TikTok and others"
অপু একটা মাগি,1,"Meme, TikTok and others"
শালায় কি মারা যাবে না,1,"Meme, TikTok and others"
মিথিলা একটা খানকি,1,"Meme, TikTok and others"
হারামির বাচ্চারে আর ওই ব‌উটারে আইনের আওতায় দেওয়া উচিৎ এমন বিচার হওয়া উচিৎ যাতে ভবিষ্যতে এই ধরনের কুলাঙ্গার সমাজে স্থান না পায়,1,"Meme, TikTok and others"
খানকির পোলারে পিটাইয়া মার,1,"Meme, TikTok and others"
হারামির ফাসি দেওয়া উচিত,1,"Meme, TikTok and others"
তোর মারে আমি চুদি,1,"Meme, TikTok and others"
খানকির ছেলের গাঁড় ভেঙ্গে দাও,1,"Meme, TikTok and others"
কুকুর টার নাম কী ঠিকানা কী অামি নিজে গিয়ে কুকুর টাকে পিটাব,1,"Meme, TikTok and others"
ছেলেরা এতো পাগল কেন,1,"Meme, TikTok and others"
তোর মারে চুদি খানকির পোলা তোর তোর ঠিকানা দে তোর মারেচুদি,1,"Meme, TikTok and others"
মাগির বেটি তোর মাকে চুদী,1,"Meme, TikTok and others"
বালের ভিডিও দেখাও খান্কি মাগির চোদোন ধরে দেয়ালে দেয়ালে শুয়োরের বাচ্চার ভিডিও,1,"Meme, TikTok and others"
তুর মতো নায়ক কে৷ চুদি না,1,"Meme, TikTok and others"
শুওরের বাচ্চা এইরকম নোংরা ছবি দেওয়া বন্ধ করে দে সালা কুত্তার বাচ্চা,1,"Meme, TikTok and others"
মাদারচোদের ফাঁসি হওয়া দরকার,1,"Meme, TikTok and others"
রাগে তো মাথাটা যন্ত্রনা শুরু করলোওই কুত্তারে গু খাওয়ানোর দরকারপ্রশাসন আর কি করবে,1,"Meme, TikTok and others"
কুত্তার বাচ্চাকে ফাসি দিয়ে দেন আর প্রতিবেশিদের অনেক ধন্যবাদ আমাদের চারপাশে যেখানেই এমন হবে ঠিক এই ভাবেই এই সকল জানোয়ার দের কে উচিত শিক্ষা দিতে হবে,1,"Meme, TikTok and others"
খানকির পুলারা জামায়াত আছে বলে দেশে ইসলাম ঠিকে আছে তদের জন্মের ঠিক নাই,1,"Meme, TikTok and others"
এমন কুলাঙ্গার ছেলে কে ফাঁসিতে দেয়া হোক,1,"Meme, TikTok and others"
জানোয়ারটাকে জুতাপেটা করা উচিত,1,"Meme, TikTok and others"
ময়ূরী তো ফাকিং গার্ল শালিদের লজ্জাও নেই,1,"Meme, TikTok and others"
এই রেন্ডিমাগী তুই এখন কত টাকা নিয়ে গুদমারা জানাবি তোর রেট বেড়ে গেছে নাকি জাকির নায়েক সম্বন্ধে মিথ্যা মিথ্যা কথা বলার জন্য শিয়ারা তোকে কত টাকা দেয় তাড়াতাড়ি জবাব দে বেশ্য়া মাগী,1,"Meme, TikTok and others"
নাস্তিক চ্যানেল নাস্তিক তুই শয়তান মাগি,1,"Meme, TikTok and others"
হালায় মানুষের বাচ্চা না,1,"Meme, TikTok and others"
এই খানকী মাগী ওআইসি ভারততের পখো নিয়েছে তুইপাইলিকই,1,"Meme, TikTok and others"
এই খানপোলারে ফাসি দেয়া দরকার এরকম ছেলেকে কুত্তার মত করে মারা দরকার,1,"Meme, TikTok and others"
মালুর জাত তোদের কচুকাটা করা হবে খুব শীঘ্রই ইনশা আল্লাহ্ বাবরি মাসজিদ কেন গোটা হিন্দুস্তান দখল করবো আমরা মুসলিমরামুসলিমদের ভয়ে সব জায়গার নাম পরিবর্তন করছে গোবর খোর মালুরা,1,"Meme, TikTok and others"
কুকুর বিড়ালকে আশরয়দিলে যেমনমাথায়ওঠে নাচেরানুদি ঠিকতাই ওকে বের কোরে দাওআমি খুসিকারন যেমানুষ কে ভালোবাসেনাসে উপর ওলাকেউভালোবাসেনাবেইমানওকে আবাররাসতারভীকারীবানিয়ে দাও,1,"Meme, TikTok and others"
খানকির পুলা তোর কাছে পেলে নটির বাচ্ছা নামাজ নিয়ে কথা বললি কেনো,1,"Meme, TikTok and others"
আরে গাদার বাচছা মুসুলমান কেন তর দেশে কেন যাবে,1,"Meme, TikTok and others"
এই রাম ছাগল এইটা কি অপু এইটা তো অনন্য মেয়ে আর এইটা কি শাকিবের হাত এইটা তো অনন্য লোকের হাত সঠিক খবর বলতে না পারলে ঘরে বসে থাক,1,"Meme, TikTok and others"
তোর গুস্টি চুদে আমার পোলায়,1,"Meme, TikTok and others"
খানকির পোলা তোরে সামনে পাইলে খুন কইলা ফালাই তাম,1,"Meme, TikTok and others"
কুকুরের মতো দেখা যাচ্ছে,1,"Meme, TikTok and others"
সানাই মাগি নিয়ে ভিডিও করলে তুমিও সেই রকম,1,"Meme, TikTok and others"
এই খানিকর বাচ্ছার খবর সব মিওা এক মাস ধরে একি খবর দেছ ঝুদ্ধ শুরু পাকিস্তান দখল করছে কাস্মীরী বাধ্নির বাচ্ছা তুরে চুদি তোর মারে চুদি খানকির বাচ্ছা,1,"Meme, TikTok and others"
শালার ব্যাটা তার ছিড়ে একগানের কান্দার গান,1,"Meme, TikTok and others"
সালা মালায়নের জাত কই কারে,1,"Meme, TikTok and others"
ওই সালেক কেটে ফেলা উচিৎ,1,"Meme, TikTok and others"
শালা চরিত্রহীন,1,"Meme, TikTok and others"
খানকির পোলা৷৷ নামাজ নিয়া কথা কবি না,1,"Meme, TikTok and others"
ওরে চুদে মজা লাগবে না,1,"Meme, TikTok and others"
দুধ আর দুধ ভিলো,1,"Meme, TikTok and others"
পতিতা আর কি বলবে,1,"Meme, TikTok and others"
ওই কানকির পোলা গরিপ কি তোর মারে কি মোদ খাইহা চোদছে,1,"Meme, TikTok and others"
এই জানোয়ারটা কে ধরে ইচ্ছা মতো পিটিয়ে হাতপা কেটে দেওয়া উচিত,1,"Meme, TikTok and others"
দেশি মাগী,1,"Meme, TikTok and others"
হে আল্লাহ এমন সন্তান যেন কোন বাবা মায়ের পেটে না হয় এতো সন্তান না এই হলো আসল জানোয়ার এই কুত্তার ছেলে ও এই মুরুব্বি কালে এমনি থাপ্পড় মারে যেন হে আল্লাহ তুমি এই লোকটা হাত পগ্গো করে দাও তুমি বিচার করো,1,"Meme, TikTok and others"
যে দেশে যুদ্ধ হচ্ছে তার মনে নেই আর শালা ইউটিউবারদের ঘুম নেই যত শালা ফেক নিউজ ইন্ডিয়ার আছে তো পাকিস্তান মশা চাপ করে দিলে মরে যাবে,1,"Meme, TikTok and others"
ময়ুরির দুধ গুলা দেখিনি অনেক দিন দরে,1,"Meme, TikTok and others"
কুতার বাচ্চা নামাজ নিয়ে কথা বলি কেনো,1,"Meme, TikTok and others"
মিননির মত মাগীর ফাঁসি হয়া উচিত,1,"Meme, TikTok and others"
লেওড়ার ডাক দিলোপুটকিতে লেওড়া ডুকিয়ে চিরে দেবো মুসলমান মাগিদের,1,"Meme, TikTok and others"
ওই কানকির পোলারে কাছে পাইলে মাইরাই ফালতামকত বড় স্পর্দা বাবার গায়ে হাত তুলে,1,"Meme, TikTok and others"
শাস্তি কামনা করি চরম এই সালা টার,1,"Meme, TikTok and others"
আহা রে খানকি মাগী,1,"Meme, TikTok and others"
খানগির পোলা খাইতেছোস কোক আর কস মদ হোগাই লাথি দিবো চুরির ভাই,1,"Meme, TikTok and others"
ফালতু সময় নিয়ে কাজ নাই যতসব ফালতু কথা তুর নিউজ চুদি খানকির পোলারা জুতা মার মিথ্যা কথা বলা জন্য তুই খানকির মাগী ফালতু,1,"Meme, TikTok and others"
হে আল্লাহ এমন জানোয়ার সন্তান কোন মায়ের গর্ভে জন্ম দিও না,1,"Meme, TikTok and others"
এই ছেলে কে মেরে ফেলা হক সালা মাদার চুদ তাকে এমন অবসা করেনন জা দেখে সারা জিবনে জন্ন্য মনে রাখে তাকে জুতা পিটা হক,1,"Meme, TikTok and others"
এই জানোয়ার তার হাত কেটে দেওয়া হোক,1,"Meme, TikTok and others"
এক কথায় হারামী ইসলাম নিয়ে অনেক আপুত্তি কর মন্তব্য দেখিছি,1,"Meme, TikTok and others"
ছেলে না কাপুরুষ সালা বোকাচাদা,1,"Meme, TikTok and others"
এই জানোয়ারের বাচ্চা জেথাই থাকুক না কেন ওকে ধরে এনে ফাসি দেওয়া উচিৎ,1,"Meme, TikTok and others"
জীবনে বাপ্পির একটা গান তার সাথে একটা মুভিও দেখি নাই সালা একটা আবাল ও নায়ক হয়ন ক্যামনে বুঝিনা বোকাচুদার বাল,1,"Meme, TikTok and others"
তুই যে একটা পতিতা তোর কথা শুনে বুঝা যায়,1,"Meme, TikTok and others"
এই কুকুরকে অনেক অনেক কঠিন শাস্তি দেওয়া উচিত তার সাথে তার বউ কো শাস্তি দেওয়া উচিত,1,"Meme, TikTok and others"
তোরা কোথাকার পাগল চোদা রে ঈশ্রায়েল আরবের ঐতিহ্যবাহী মসজিদ কে নাইট ক্লাব বানিয়েছে আর সৌদি আর ইরান আসবে ভারতের বাবরি মসজিদ দখল করতে ওরে পাগল চোদা তোদের সাথে তর্ক করা বৃথা ভারতের কাছে যে সমস্ত পারমাণবিক অস্ত্র আছে তার দুটো ইরান সৌদি তে ফেললেই ওরা বুঝে যাবে,1,"Meme, TikTok and others"
সালা কুতা তোকে পেলে মেরে শূইয়ে দিতাম,1,"Meme, TikTok and others"
আবালডারে নায়ক বানাইছে কেডা,1,"Meme, TikTok and others"
বানচোদকে ফাসি দেওয়া উচিত,1,"Meme, TikTok and others"
তুই মাগি আর তোর মারে কুত্তা দিয়া চুদাইতুই মাগির কুত্তা দিয়া চুদানোর ভিডিও আমি পাইচি,1,"Meme, TikTok and others"
বোকাচোদা বাংলাদেশ বোকাচোদা শালা কুত্তার বাচ্চার ভিডিও কেনরে,1,"Meme, TikTok and others"
এই খানকির পোলারে ফাঁসি দে,1,"Meme, TikTok and others"
দুদের যেই চাইজ,1,"Meme, TikTok and others"
এ মাগি বিদেশে চুদা দেয়,1,"Meme, TikTok and others"
হে আল্লাহ এটা কি দেখলাম পৃথিবীতে কি শুরু হয়েছে এই জানোয়ারের উপর আল্লাহর গজব পড়ে না কেন,1,"Meme, TikTok and others"
কুকুর টা কে হাতের কাছে পাইলে পা আর হাত ভাঙ্গতাম যাতে কোন দিন আর সোজা হয়ে দাঁড় তে পারতো না,1,"Meme, TikTok and others"
দূর হ খানকি মাগি,1,"Meme, TikTok and others"
তোমাদের চোদা উচিত,1,"Meme, TikTok and others"
শয়তানের বাচ্চা কুত্তার বাচ্চা ফাঁসি দেওয়া দরকার,1,"Meme, TikTok and others"
বুদার নায়ক হিজরা,1,"Meme, TikTok and others"
খানিকির পুএরে পাইলে তারে জুতা দিয়ে পিটাইতাম,1,"Meme, TikTok and others"
কি বলব ভাষা হারিয়ে ফেলেছি জানোয়ার কে হার মানায় সালা কুত্তা তাকে জবাই করা দরকার,1,"Meme, TikTok and others"
এর হাত দুইটা কেটে ফেলা দরকার,1,"Meme, TikTok and others"
একটা জানুয়ার দেখলাম সাথে একটা মহিলা জানুয়ার,1,"Meme, TikTok and others"
বিচার চাই এই জানোয়ারের,1,"Meme, TikTok and others"
হারামখোর মহিলা একটা ভক্তদের গায়ে গন্ধ এটা কোন শিল্পী কে বলতে শুনিনি আমি ভাগাড়েই থাকা উচিৎ ছিল তার,1,"Meme, TikTok and others"
মাগি তূই এক রাতের জন্য কত টাকা নিবি,1,"Meme, TikTok and others"
জাহান্নামের খাতাই এতো সুন্দর মেয়েটির নাম টাও এই শুয়োরের বাচ্চারা লিখিয়ে দিলো শুয়োরের বাচ্চারা নিজেরাও ন্যাংটা অন্য কেও ন্যাংটা বানাতে চাই,1,"Meme, TikTok and others"
জানোয়ারের ফাসি চাইএই পশুর বাড়ি কই,1,"Meme, TikTok and others"
এগুলি রেন্ডিয়া মাদারচোদ দারা সম্ভাব,1,"Meme, TikTok and others"
আপনি থিকিই বলছেন মেমআপনার সাথে আমি একমতআমি সাকিব খানকে খুব তাড়াতাড়ি অপু দিদি সাথে কথা বলে দেখতে চাই,1,"Meme, TikTok and others"
মিথিলা হচ্ছে একটা বেসসা খানকি মেয়ে,1,"Meme, TikTok and others"
মাদারচোদ তুই নামাজ নিয়ে কথা বলতেচোদ কেনো,1,"Meme, TikTok and others"
তোর বউরে চুদে শিবির,1,"Meme, TikTok and others"
এই মাগি তাছলিমার নাছরিন ভারতের হিন্দু নরপশু হানুদ মালাউনদের চুদা খাইতে খাইতে এখন সখ জাগছে ঘোরার চুদা খাইতে তাকে বাংলাদেশ সরকারের মাননিয় প্রদান খানকি বেশ্যা মাগি হাসিনার পক্ষ থেকে একটি ঘোড়া দেওয়া হউক,1,"Meme, TikTok and others"
ভারত কে টুকরা করে দাও পাকিস্তান মুসলিমের বাল ও চিরতে পারবেনা নাস্তিক মোদি,1,"Meme, TikTok and others"
এই খানকি মাগী রা তোদের মাকে চুদবে,1,"Meme, TikTok and others"
এই শুয়োরের বাচ্চাকে এর ছেলে এভাবেই একে দিন পিটাবে,1,"Meme, TikTok and others"
শাওন মাহমুদ নামে একটা মাগি পাওয়া গেছে,1,"Meme, TikTok and others"
শুয়ারের বাচ্চা তর ছেলে একদিন তোকে এভাবে চড়াবে,1,"Meme, TikTok and others"
তোমার সঙ্গে কথা বলার সুযোগ দিবেন প্লিজ তোমার বড় বড় দুধ গুলো আমার অনেক ভালো লাগে কল ইমু,1,"Meme, TikTok and others"
মেসি তর মাকে চুদেনাই,1,"Meme, TikTok and others"
এই চেনালের মারে চুদি খানকীর পোলা তোর কাছে আর ভিডিও ছিলো না খানকীর পোলা,1,"Meme, TikTok and others"
আরে এগুলা হিজলা মাগি,1,"Meme, TikTok and others"
সিফাইতা মাদারচুদ তরে আমি চুদি,1,"Meme, TikTok and others"
তুই হলে একটা পতিতা,1,"Meme, TikTok and others"
এই বাইনচোদের বাচার কোনো অধিকার নাই🤬 ওরে ফাঁসি দেওয়া দরকার,1,"Meme, TikTok and others"
শালা কি সব আজে বাজে ভিডিও,1,"Meme, TikTok and others"
পাগল কে যদি সোনার থালায় খেতে দেওয়া হয় তবে সে মনে করবে আমি ভালো আর বাকি সোভাই পাগল,1,"Meme, TikTok and others"
মাদার চোদ ছেলেটাকে মার,1,"Meme, TikTok and others"
বুজুর্গ লক বলে থাকেন শুয়োরের মাথাই সিনদুর সবাই না,1,"Meme, TikTok and others"
তর মা কে তুই ছদ,1,"Meme, TikTok and others"
তোদের চোদে কিডা ওসুধের বুল্লিনে তোর আর এক ভাতার বলবে,1,"Meme, TikTok and others"
বিয়াদব শালার পুত আজ কোথায় এরা,1,"Meme, TikTok and others"
শালা কুত্তার বাচ্চা তুই নামাজ কে নিয়ে গালি দেস তোর গালে জুতা মারব কুত্তার বাচ্চা তুই মুসলিমদেরকে গালি দিস কেন নামাজ পড়তে অপরাধ কি করেছে শালার পো শালা তুই মানুষের ঘরে জন্ম নেয় কুকুরের ঘরে জন্মায় তাই তুই মুসলিমদের নামাজকে অপমান করিস তোকে পাইলে কবুতরের মত ছিঁড়ে কাওয়াকে কুত্তাকে দিয়ে খাওয়াইতাম,1,"Meme, TikTok and others"
জানোয়ার একটাকারো যেনো এমন কুলাঙ্গার সন্তান না হয়,1,"Meme, TikTok and others"
মদি মা কে চুদি মাদারি চুদ,1,"Meme, TikTok and others"
শালা তো জানোয়ার,1,"Meme, TikTok and others"
তোর মায়েরে চুদদে গিয়ে ধরা খাইছে বঙ্গবন্ধু তুই খানকির পোলা,1,"Meme, TikTok and others"
হালা তুই নিজেই জারোয,1,"Meme, TikTok and others"
শালীরে জুতা মার,1,"Meme, TikTok and others"
তোমার নানীর কত ছিল তোমার মার কত ছিল তোমার কত আছে এটা ইনবক্সে জানাও,1,"Meme, TikTok and others"
মার অই ছেলে রে বাইনচুদ ছেলে,1,"Meme, TikTok and others"
ও মাগী,1,"Meme, TikTok and others"
তোদের কি কুত্তায় পুন মারছেনি বেইমানের বাচ্চারা,1,"Meme, TikTok and others"
রেশমির ঠোঁটের উপরে জুতার বাড়ি দেওয়া হোক,1,"Meme, TikTok and others"
এই শালার পুতেরা মারমু,1,"Meme, TikTok and others"
সালার হাত কাটা হোক,1,"Meme, TikTok and others"
এই মাগির সম্পূর্ণ ভুয়া খবর ওই ম তোর বাসা কোথায়,1,"Meme, TikTok and others"
সালা একটা মাদার চোদ,1,"Meme, TikTok and others"
তর সাইজ কত,1,"Meme, TikTok and others"
কুকুরের গুয়া থেকে ঘুরে এসেছে এই চেনেল,1,"Meme, TikTok and others"
তোদের মিথ্যা খবরের মায়ের গুদ মারি হাজার মার্কিন সেনা কাশ্মিরে কি গাড় মারাতে ঢুকেছে রে খানকি মাগি তোরা খবর বানাস না খবরের মা কে চুদে পেট বানাস ভারতের পার্লামেন্টে কে হামলা কোরেছে রে বুকিচুদি তাকে বোলিস মোদীর দুটো পাকা বাল ছিড়ে আনতে তাহলে বুঝবো বাপের বেটা,1,"Meme, TikTok and others"
শালা মোদি,1,"Meme, TikTok and others"
এটা তো মাগী চোদা চ্যানেল,1,"Meme, TikTok and others"
ওর দুই গালে দুইটা চটকানা মারা উচিত যে ভাবে বাবাকে মেরেছে জানোয়ার,1,"Meme, TikTok and others"
সব ভুয়া খবর এই বাংলাদেশি মাগির কেউ দেখবে না,1,"Meme, TikTok and others"
জানোয়াড়ের চড় গুলা আমার গায়ে লাগতেছে,1,"Meme, TikTok and others"
বাল আর বালের খবর বোকাচুদারা,1,"Meme, TikTok and others"
তোরা কোন ধরনের বোকাচোদা রে,1,"Meme, TikTok and others"
ধম নিয়ে কতা বলবিনা খানকির বাচচা,1,"Meme, TikTok and others"
জানোয়ারটার ফাঁসি চাই,1,"Meme, TikTok and others"
খানকির পোলরে জন্ম না দিয়া কুত্তার বাচ্চা জন্ম দিলে ভালো হতো,1,"Meme, TikTok and others"
এই পাঠাকে ধরে পিটাও,1,"Meme, TikTok and others"
খানকির বাচ্চারা দেশটাকে শেষ করছে,1,"Meme, TikTok and others"
ও পাগল,1,"Meme, TikTok and others"
ফাসি দেওয়া দরকার শালাকে,1,"Meme, TikTok and others"
সালাতুইএকটাখানকিরবাচাসালাবাবাকেমারছিশতোরহাতইঠবেনা,1,"Meme, TikTok and others"
তুইতো মাগি সালি খানকি,1,"Meme, TikTok and others"
তোকে জুতা দিয়ে পেটানো উচিত কুত্তা চুদি মাগী কবে চিনের সেনা ঢুকেছে তোরা যে নিজেদের কতবড়ো জ্ঞানী মনে করিস,1,"Meme, TikTok and others"
তোমার সাথে সেক্স করা যবো,1,"Meme, TikTok and others"
তোরে কাছে পাইলে শুয়ার দিয়া চুদাইতাম,1,"Meme, TikTok and others"
তোমাকে চুদার কোন তরিকা বল মাগি,1,"Meme, TikTok and others"
এই মাদারচোদ এর বিচার হওয়া ওচিত,1,"Meme, TikTok and others"
এ খান্কি মাগির বারবার একটা কথা কওন লাগে,1,"Meme, TikTok and others"
এটা তো একটা মাগি,1,"Meme, TikTok and others"
মাদার চোদ খানকির পোলা নামাজ নিয়া গালি দিলি কেনো,1,"Meme, TikTok and others"
রানু পাগলি ও তার মেয়ে কে জুতা মারা উচিত,1,"Meme, TikTok and others"
মানুষ না তুই বড় যানুয়ার,1,"Meme, TikTok and others"
প্রথমেই ঃ জানতে চাই আপনার এমন মহত উদ্দেশ্যে র মানে কি য় প্রশ্ন ঃ আপনি এই নায়িকাদের ব্রার সাইজ কি মেপে এসেছেন য় প্রশ্ন ঃ মেম 🤪🤪আপনার ব্রার সাইজ কতো উত্তর জদি না দেন বুঝে নিব আপনি একটা,1,"Meme, TikTok and others"
এই কুত্তার বাচ্চাদুই টাকা ইনকাম করার জন্য ভুল সংবাদ দিস কেনমাগির পুলা,1,"Meme, TikTok and others"
জানোয়ারের ডান হাত কেটে দাও,1,"Meme, TikTok and others"
এই কুকুর টাকে সর্বচ্চ শাস্তি দেওয়া হোক,1,"Meme, TikTok and others"
কুত্তার বাচ্চারে কেটে রাস্তার কুকুকে খাওয়ানো উচিত 🤬🤬🤬,1,"Meme, TikTok and others"
এটা তো গুলিস্তানের টেকা দামের ভুসকি মাগি,1,"Meme, TikTok and others"
সাকিবের ভোনেরে চুদি,1,"Meme, TikTok and others"
দেশি ভাবি রা গুদের জালা মিটাতে,1,"Meme, TikTok and others"
তুই আমার বালের বাল,1,"Meme, TikTok and others"
ফালি চাই এই শালার,1,"Meme, TikTok and others"
খানকীর পোলা,1,"Meme, TikTok and others"
খানকির পোলারে ফাসি দেয়া হোক,1,"Meme, TikTok and others"
শালারে যে পাইলে কি করতামআল্লাহ তাকে ধংস করে দাওএমন শাস্তি দেও যাতে দুনায়ায় কেউ বাবা মাকে এমন করতে না পারে,1,"Meme, TikTok and others"
অকে আমার মতে ঘুড়ি কাটা বন্দা করে এক মাস পিটানো দরকার হারাম যাদা ছেলে,1,"Meme, TikTok and others"
ফকির মাগী কে আবার ভিখারী করে দাও,1,"Meme, TikTok and others"
কুত্তা দিয়া চুদাইলে তো ধোন আটকায়া যাইবো,1,"Meme, TikTok and others"
বেষসার সন্তান তোর মাইরে চুদি বার,1,"Meme, TikTok and others"
প্রতিটা থাপ্পড় আমার কলিজায় লাগছেআমি মুসলিম হয়েও আমি ওকে শেষ করে দিতাম জানোয়ার মানুষ থু শালা শালা হিজলা বউয়ের কথায় চলে শালার পা কেটে দিলে হবে,1,"Meme, TikTok and others"
কুত্তার বাচ্চা নামাজ নিয়া গালি দিবি না শালা মাদরচুদ,1,"Meme, TikTok and others"
নামাজ নিয়ে কথা বল্লে তোকে তোর কুত্যা দিয়ে খাওয়াবো,1,"Meme, TikTok and others"
সালাকে কাছে পাইলে পাছা দিয়া গরম রট দিতাম,1,"Meme, TikTok and others"
কুত্তার বাচ্ছা আমাদের নিয়ে কথা বল আমার ণবী কে নিয়ে একটা কথা বলবি তোকে পাইলে তোকে মারার জন্য আমিই যথেষ্ট শুয়েরের বাচ্ছা,1,"Meme, TikTok and others"
তোর একটা বিকিনি পরা ছবি দিছ খানকি,1,"Meme, TikTok and others"
ভাষা শুনে তো মনে হয় হারামির বাচ্চা কলকাতার হবে আর বাংলাদেশের কুলাঙ্গার গুলা শিরোনাম বানিয়ে বাংলাদেশের চ্যানেলে প্রচার করছে এটার মাধ্যমে বাংলাদেশের কিছু কুলাঙ্গার ছেলেপেলে মাবাবার উপর অত্যাচার করা শিখবে এই সমস্ত ভিডিও আপলোড না দেয়াই ভালো,1,"Meme, TikTok and others"
সালারে ফাসিতে ঝোলানো উচিত,1,"Meme, TikTok and others"
তোর মার আর তোর মেয়ে থাকলে ওরে চুদ্মু তোর ধন কাইটা ফালামু,1,"Meme, TikTok and others"
শুয়োর একটা আল্লাহ তোক জাহান্নাম এ দিবেদুনিয়ায় আল্লাহ তোক গজব দিক,1,"Meme, TikTok and others"
এই কুলাঙ্গার ছেলেটার ফাঁসি চাই,1,"Meme, TikTok and others"
তোর মারে চুদি খানকির পলা দালাল,1,"Meme, TikTok and others"
কানকী ম্যাগী এটা কি চ্যালেন,1,"Meme, TikTok and others"
সালা চাপাবাজ,1,"Meme, TikTok and others"
এই জানোয়ার টার ওই হাত কেটেদেয়া দরকারছি,1,"Meme, TikTok and others"
মাগি মনে হয়ে,1,"Meme, TikTok and others"
এই শোওরের বাচ্চা কে গুলি করে মারা হউক,1,"Meme, TikTok and others"
তোকে চুঁদতে আসছে আমেরিকার সেনারা শালি,1,"Meme, TikTok and others"
তুমি চুদির পো লোপার সোনা চাটো,1,"Meme, TikTok and others"
ভাবী তোমার হট দেবর আমি কেমন আছেন আপনি মিস দাও,1,"Meme, TikTok and others"
ছেলে ছেলের বউ জানোয়ারের চেয়ে ও খারাপ,1,"Meme, TikTok and others"
ওই খানকির পোলা সেপাতুল্লা নামাজ নিয়ে কথা কইছস তোর গুষ্টি চুদী তোর বউরে চুদী তোরে চুদী তোর মাইয়ারে চুদী তোরে কুত্তা দিয়া চুদামু খানকির পোলা নামাজ নিয়ে আর খারাপ কথা বলবি না,1,"Meme, TikTok and others"
এই খানকির পোলারে জন্ম দিছে কেমনে রে ভাইঅসভ্য অসুস্থ মাদারচোদ তুই রাস্তা ঘাটে মইরা পইরা থাকবিকুত্তাও তোরে তখন চোদবেনা,1,"Meme, TikTok and others"
তোমাকা চুদবা,1,"Meme, TikTok and others"
বাংলাদেশে হলে ওর লাশ ও খুযে পাওয়া যেতো নাবালের প্রশাসন চোদায় হালার পো হালা বাবার এক বিন্দু শুক্র থেকে তোর জন্মসেই বাবার গায়ে হাত কেমনে তুলিসহায় আল্লাহ আস্তাগফিরুল্লাহ,1,"Meme, TikTok and others"
হাফ প্যান্ট পরার থেকে পোদ খুলে ডিউটি করা ভালো কিন্তু চাকরি ছাড়া যাবে না,1,"Meme, TikTok and others"
হারামি টাকলা বুড়া তুই মদ খাই নাই গু খাই শয়তান তোর মুখের ভাষা এতোই খারাপ ছিঃ ছিঃ ছিঃ এই হারামি নাস্তিক তোর এই নাফামাজি মুখে পোকা পুরো তোর মুখে জুতা মারি খানকির পোলা এই শূয়রের বাচ্চার মুখে সবার জুতা মানেন হারামি কিভাবে মুখ খারাপ করে ছিঃ ছিঃ ছিঃ,1,"Meme, TikTok and others"
এই মাদার চোদের বাড়ি কোথায়,1,"Meme, TikTok and others"
সেফু তোর মায় আমারে চুদে,1,"Meme, TikTok and others"
এই শালাকে ফাসি দেয়া উচিত,1,"Meme, TikTok and others"
সালার পুত তর হোগা কাইটা লামু নবিরে নিয়া কিছু বললে,1,"Meme, TikTok and others"
তর মা বইনেরা মানুষে চুদেনা মনে হয় বিদেশী কুত্তা চুদে,1,"Meme, TikTok and others"
শালারে ইচ্ছা মতন পিটাইতে মনে চায় সাথে ওর বৌওটারে কারন কিছু না বলে দারিয়ে দেখতেছে,1,"Meme, TikTok and others"
কুত্তারে পাবলিক এর সামনে ফাসি দেওয়া হক,1,"Meme, TikTok and others"
একে খোলা রাস্তায় পিটানো উচিত,1,"Meme, TikTok and others"
দেখা যায় নিশা সওদাগরের মত লুইচচা সালা সাকা,1,"Meme, TikTok and others"
তুমি সেক্স ফিলিম কর,1,"Meme, TikTok and others"
কাংকির পুলা তোরে আমি পাইলে বডি থেকে মাথা আলাদা করে দিতাম,1,"Meme, TikTok and others"
এই মাগী টা কে দেখলেমন টা কয় টা জুতা মারি,1,"Meme, TikTok and others"
তোরে মাইরা জেলে জামু আমি মাদারের বাচচা,1,"Meme, TikTok and others"
রেশমী মেয়ে নাকি মাগি,1,"Meme, TikTok and others"
এসব না করে সাকিব এর কাছে গেলেই ত অপুর মতো বড় সানাইকে ও বড করে দিতও,1,"Meme, TikTok and others"
তুমি যে খাংকি আবার অন্যর ফেমেলি দেকতে চাস,1,"Meme, TikTok and others"
নয়নের মা একজন বেশসা,1,"Meme, TikTok and others"
উনাকে উচিত শিক্ষা দেওয়া হোক এই জানোয়ারের বাচ্চা যেন এরকম কাজটা করে,1,"Meme, TikTok and others"
জানোয়ারের বাচ্চাকে আগে জোরছে থাপ্পর মারা উচিৎ ছিলো,1,"Meme, TikTok and others"
ওরে কি বলবো কত্তা,1,"Meme, TikTok and others"
তোর মার ভোদার খবর খানকী মাগী,1,"Meme, TikTok and others"
এই কুকুরের বাচ্চাকে পিটিযে মেরে ফেল সবাই,1,"Meme, TikTok and others"
এইরকম ছেলেকে জনতার মঞ্চে ফাঁশি দেওয়া হোক,1,"Meme, TikTok and others"
হালার পোলা বদমেশ আবার নায়ক নাকি দেখতেতো দারোয়ানের মতো লাগে,1,"Meme, TikTok and others"
তোকে কুকুর দিয়ে চুদাবো খানকি মাগি,1,"Meme, TikTok and others"
শালার হারামজাদাকে মেরে ফেললোও রাগ মিটবে নাহ,1,"Meme, TikTok and others"
এই জানোয়ার টাকে ফাঁসি দেওয়া দরকার,1,"Meme, TikTok and others"
মদ খাও অার মা‌ঘি চু‌দো ব,1,"Meme, TikTok and others"
কিরে এডমিন শালা কুত্তার বাচ্চা এই ভিডিওটা বছর আগের আর তুই হেইড লাইন কি দিচ্ছ,1,"Meme, TikTok and others"
মদ খাইয়া আমি তর মাকে চুদবো,1,"Meme, TikTok and others"
এসব ছেলে মেয়ে কে জলান্ত আগুনে পরানো হক,1,"Meme, TikTok and others"
দুদ দুইটা বিশ কেজি হবে,1,"Meme, TikTok and others"
কুতার বাচ্চা সব গুলা,1,"Meme, TikTok and others"
পাগলের বাচ্ছামাদারচোদের বাচ্ছারে দরে নেংটা করে পিটানো দরকার ছিল,1,"Meme, TikTok and others"
ওই খানকির পোলা বাইনচোদতোরে কাছে পাইলেদুই ভাগ করতামসালা মাইন্দারের পো,1,"Meme, TikTok and others"
কুত্তার বাচ্চারে আল্লাহ এখনো বাঁচায় রাখছে কেনমাদারচোদ,1,"Meme, TikTok and others"
সালা চ্যামার কে জুতা দিয়ে পিটান দরকার,1,"Meme, TikTok and others"
কেউ এর বৌকে মার মাগি চেয়ে চেয়ে দেখছে শালি কিছু বললো না,1,"Meme, TikTok and others"
শালার বাচ্চা মহিলার ব্যপারে মহিলাদের ইত বলা উচিৎ তোর কি,1,"Meme, TikTok and others"
এই কুকুর টাকে পুলিশে দেন,1,"Meme, TikTok and others"
দুধের সাইজ টা খারাপ নাতোমার সেক্স করা দেখেছি,1,"Meme, TikTok and others"
এই ছেলেকে জুতা মার সবাই,1,"Meme, TikTok and others"
খাক্কির পোলা,1,"Meme, TikTok and others"
তোর জাতেরে হালাই চুদমু এক ঠেং কাদে নিয়া,1,"Meme, TikTok and others"
সেলিম মাদারচোদ টা কাফের,1,"Meme, TikTok and others"
কুত্তার বাচ্চার গর্দান কাটা উচিত,1,"Meme, TikTok and others"
মধু খেয়ে এখন ছেরে দিলো বানচুদে,1,"Meme, TikTok and others"
মাদারচুদ্দ তোর বাড়ির পাশে আমার বাড়ি থাকলে তোর ভেজাল ছিলো রে বেঁচে গেলি রে,1,"Meme, TikTok and others"
তোরে চুদমু,1,"Meme, TikTok and others"
এই সালাকে গুলি করে মারা দরকার,1,"Meme, TikTok and others"
ভিডিওতেই জানোয়ারটাকে গনপিটুনি দিয়ে আধমরা করলে খুশি হতাম,1,"Meme, TikTok and others"
ও তো কুত্তার চেতেও খারান ও যে হাত দিয়ে মারছে সেই হাত দুটো কেটে দেওয়া হোক,1,"Meme, TikTok and others"
তর মায়েরে তুই চোদ তর ধন কাইট্টা তরে এলিএন দিয়া চোদামু খানকি মাগির পোলা,1,"Meme, TikTok and others"
বাংলার পতীতা,1,"Meme, TikTok and others"
মুখে জুতামেরে রানুর মেয়েকে ভাগাও ওর তো টাকার অভাব ছিল না মা ভিক্ষাকরে খেয়েছে লজ্বা কোরছে না এখন ঝাটা মেরে দুর করো,1,"Meme, TikTok and others"
সালা খবিশ তোর কিছু আছে সালা মিথ্যা বাধি,1,"Meme, TikTok and others"
সরকারের কাছে এই জানোয়ারের বিচার চাই,1,"Meme, TikTok and others"
সালা আবালে নাকি নায়ক হা হা,1,"Meme, TikTok and others"
খানকির পোয়ার কোনো ক্ষমা নাই স্যালুট প্রশাসন,1,"Meme, TikTok and others"
মাদারির ফাঁশি চাই,1,"Meme, TikTok and others"
মুসলিম মারো জংগি শেষ করো আর এই মাগি শুধু মিথ্যা খবর বলে,1,"Meme, TikTok and others"
শালা সমাজে মুখ দেখাবে কিকরে ওকে গলায় দড়ি দিতেই হবে,1,"Meme, TikTok and others"
খানকি তকে চিনি,1,"Meme, TikTok and others"
আরেক মাদারচুদ বিদেশ থাইকা আরবি শিখছে মাগিরে আরবি শিখায় সালার পুত,1,"Meme, TikTok and others"
এই মাগি এখন কার ছবিতে কি ছোট পোশাক পরে না,1,"Meme, TikTok and others"
কুত্তার বাচ্চা তোরে সামনে পেলে ব্রাশফায়ার করে মারবো,1,"Meme, TikTok and others"
এই খানকির পোলা তরে যদি পাইতাম কুত্তার মত পিটাইতাম জানোয়ার তর হাতে যেনো পচন ধরে মাগির ভাউরা,1,"Meme, TikTok and others"
শালার বেটাকে দিনের রিমান্ডে নিয়ে চরম শাস্তি দেয়া উচিত যাতে এই বেয়াদবি না করে,1,"Meme, TikTok and others"
জানুয়ারের বাচ্চাএমন সন্তানরে জন্মের সময় গলা টিপ্পা মাইরা ফেলা দরকার ছিল,1,"Meme, TikTok and others"
শালা বাপ মরলে বুঝবি বাপ কি জিনিস,1,"Meme, TikTok and others"
তোর গূদ মারতে গেলে বিএসএফ ভারতের সেনা,1,"Meme, TikTok and others"
তোমার ব্রা সাইচ কত,1,"Meme, TikTok and others"
তোর বউরে আমি গোসল খানায় দেখছি,1,"Meme, TikTok and others"
গরুর জন্য জখন মুসলমান মেরে ফেলে তখন তসলিমা কুত্তী ঘুমায় চুকানি শুরু হয়,1,"Meme, TikTok and others"
আপু ছবি করবেই শকিবও ছবি ছড়বে না,1,"Meme, TikTok and others"
তুই পতিতা মাগী,1,"Meme, TikTok and others"
শুয়োর ক্ষমা চায় ওর ফাঁসি চাই বড় কোনো শাস্তি না হলে এভাবেই চলতে থাকবে,1,"Meme, TikTok and others"
চুপ কর শালী তুই কাকে খুশি করেছিস,1,"Meme, TikTok and others"
মাদারচোত কে মার বোকাচোদার,1,"Meme, TikTok and others"
মাদার চোদ বিজেপি,1,"Meme, TikTok and others"
ঐইশালার বউকে পিটানো দরকার ব্উদারিয়েআচেকেন শালীর বেটিশালি,1,"Meme, TikTok and others"
খানকির পোলা ইসলাম নিয়া কথা চুদাবি না,1,"Meme, TikTok and others"
তুইতো খানকির ছেলে মাহুন্ডা ইহুদি বুড়া চুদা তোর মারে তুই চোদ জনোয়ার তুই বাংগালী গুষ্টিকে গালি দিয়েছিস তুই নামাযকে গালি দিয়েছিস সাহস থাকলে দেশে আয় শুওরের বাচ্চা তোকে কোটি কোটি বাংগালী ও মুসলিমেরা ভাগেও পাবেনা,1,"Meme, TikTok and others"
সব খানকি,1,"Meme, TikTok and others"
পাগলি বলে কি ছাকিব খান বলতেছে কেন,1,"Meme, TikTok and others"
খানকির পোলায় একটা জানোয়ার,1,"Meme, TikTok and others"
অনেক শালার হাত কেটে দেওয়া হোক,1,"Meme, TikTok and others"
ফারহা খান নামটা পাল্টে কুত্তা নাম রাখিস আমাদের মুসলমানের টাইটেল কেনো নিয়েছিস মুসলমানের টাইটেল কেন রেখেছিস ফারহা খান মরে দেখ মসজিদ পাথরের ঘর নাকি না জান্নাত জাহান্নাম আল্লাহর কাছে চাইবো মসজিদে জুম্মার দিনে ফজর টাইমে চাইলে আল্লাহ সব মানে ফারহা খানের জন্য জাহান্নাম চাইবো এটা বলবি জাহান্নাম বলে জিনিস নাই সব বলেছিস মেনে নিয়েছি মুসলমানকে টছোট করেছিস তাও মেনে নিয়েছি মুসলমানকে মেরেছিস তাও মেনে নিয়েছি কিন্তু আল্লাহর ঘর কে পাথরের বললি এটা মেনে নিলাম না,1,"Meme, TikTok and others"
দেব তরে চুদছে মাগি,1,"Meme, TikTok and others"
মুটকি খনকি,1,"Meme, TikTok and others"
সে এখনো মানুসিক রোগী,1,"Meme, TikTok and others"
বাংলা মাগির আসল রূপ দেখুন এখানে ফ্রিতে মাল পাওয়া যায় __,1,"Meme, TikTok and others"
কে কে মোহাম্মাদ চুদির ব‍্যাটা সুপ্রীমকোট যেটা বলতে পারেনি তুই কোথায়পেয়েছিস মাদার চোদসালা কাফেরের বাচ্চা,1,"Meme, TikTok and others"
তোর কপালে জুতা পালিশ করব,1,"Meme, TikTok and others"
বেশ্যারা সব কিছুই পারেমাগী কোথাকারতাহসানের অালো গানটার সাথে জীবনটাও মিলে গেলোমাগীকে বয়কট করা হোকতার উপস্থাপনায় অামার অামি এবং অন্যকোন নাটকও দেখবোনাএতো খারাপ অার দেখিনি,1,"Meme, TikTok and others"
মাগি তোরটি শব দেশের খবর আছে,1,"Meme, TikTok and others"
এতাকে চুদা দিয়া লাগবে,1,"Meme, TikTok and others"
মাদার সুদরে ধরে এভাবে ফেটানোর দরকার,1,"Meme, TikTok and others"
এই শালা তুই জানিস টা ছবি করেছে,1,"Meme, TikTok and others"
পযসা কামালে মানুষ হওযা যাযনা জানোযার আরে এই বাপ তোকে পিথ্বিবি আলো দেখিযেছে রে জানোযার,1,"Meme, TikTok and others"
শালার হিজলার,1,"Meme, TikTok and others"
এই খানকির পোলা তোর গুষ্ঠি মারি,1,"Meme, TikTok and others"
জারজ সন্তানএই সব জারাজদের সরকার উপযুক্ত শাস্তি দেয়না বলেই দেশে আজ এতো বৃদ্ধাস্রম,1,"Meme, TikTok and others"
এই মাদার চুতরে ফাঁসি দেওয়ার উচিত,1,"Meme, TikTok and others"
কুকুরের থেকে ও নিকৃষ্ট,1,"Meme, TikTok and others"
এই কুকুর কে মারতে ইচ্ছা করতেছে,1,"Meme, TikTok and others"
ময়ূরী সোনা তোমার ঐ দুইটা এত বড় করছ বাবারে কত টন হবে,1,"Meme, TikTok and others"
কাসমেরী মেয়েরা হিনদূদের সোনা কেটে দিবে,1,"Meme, TikTok and others"
খানকিরাও প্রকাস্যে এরকম কাজ করে না,1,"Meme, TikTok and others"
হের চুলের এটা কী কাটিং সে কী মুসলমানের বাচ্চা না চিত্রনায়ক নায়িকারাকী ধর্ম বুজে নাকী যদি বুজত তাহলে বেহায়া হতনা আল্লাহর নানত তোমাদের উপরে,1,"Meme, TikTok and others"
খানকি মাগি তূদের লজ্জা লাগে না খানকি মাগি তূর ভোদা বারা ভোরে ফাটিয়ে দেওয়া দরকার খানকি মাগি,1,"Meme, TikTok and others"
শুয়ার তোকে তো গরম তেলে ভাজলেও মনে আশা মিটবেনা,1,"Meme, TikTok and others"
ব্রেস্টের সাইজ না কইরা পুরোটা কাইটা পালা তারপর সাইজ মত ডাব লাগাইয়া চলবি তাইলে দেশীয় পন্য ডাবের চাহিদা বারবো কিছু কর্মসংস্থানের সুযোগ হইবো তোদের জামাইরা মুখ দিয়া হতাশ হইবো না ডাবের পানি পাইবো,1,"Meme, TikTok and others"
বাপ্পি নায়ক হলে কুত্তাও বাঘ,1,"Meme, TikTok and others"
গুদমারানি ভাই প্রথমে কি দেখালি,1,"Meme, TikTok and others"
এই খানকির পোলারে কেউ ভাই একটু কোপাইতি আর ভিডিও করতি আমি খুব শান্তি পাইতাম ওরে খানকির পোলা তোরে সামনে পাইলে তোর পুটকি দিয়া হাত ভরে নাড়িভুড়ি বের করে ফেলতামসুয়োরের বাচ্চা কামটা কি করলিআমার ভেতরটা একেবারে কষ্টে শেষ হইলা গেলতোর মায়রে চুদি বাংলাদেশে থাকলে তোর হাত পায়ের রগ কাইটা ফেলতাম,1,"Meme, TikTok and others"
হারামিরা তোরা কতজেখারা তোগো কথায় বুজায়,1,"Meme, TikTok and others"
জানোয়ার টাকে মেরে ফেলা উচিত,1,"Meme, TikTok and others"
জানোওয়ারের বাচ্চা খানকির পোলা,1,"Meme, TikTok and others"
ওরে জবন শুয়োরের বাচ্চা মাননীয় মোদিজীর নামে উল্টোপাল্টা কথা বলবি না তোদের আদি পূর্বপুরুষেরা হিন্দু ছিল সেটা কি জানিস কুত্তার বাচ্চা তোদের ইসলাম ধর্ম সৃষ্টি হয় মাত্র চোদ্দশ বছর আগে বাংলাদেশের যে সমস্ত হিন্দুরা তাদের কাঁধে কাঁধ মিলিয়ে পাকিস্তানের অত্যাচারের হাত থেকে তোদের কে বাঁচিয়ে ছিলো কিন্তু তোরা যেমন বেইমানের বাচ্চা সেই সমস্ত কথাগুলি এগিয়ে হিন্দুদের উপরে অত্যাচার করতে করতে তাদের মা বোনের উপরে অত্যাচার করে রেপ করে তোরা তাদের ভারতে তাড়িয়ে দিয়েছিসআরে ভারত বর্ষ তোদের কোন কালেই ছিলনা এই ভারত বর্ষ হাবি হিন্দুদের সনাতন ধর্মের লোকদের ছিল তোরা বাইরে থেকে এসে তোরা লুটতরাজ করে চোরের মত কাপুরুষের মতো ভারতবর্ষে প্রবেশ করেছিস তবে শুনে রাখ ভারতবর্ষ হিন্দুদের ছিল হিন্দুদের আছে ভবিষ্যতে হিন্দুদেরই থাকবে বুঝলি হারামজাদারা,1,"Meme, TikTok and others"
মৌয়ুররী খানকি মাগী,1,"Meme, TikTok and others"
এমন কুত্তা বেঁচে আছে কি ভাবেলজ্জা হওয়া উচিত,1,"Meme, TikTok and others"
সাকিব লুচ্ছা,1,"Meme, TikTok and others"
ওর এক পা চট্টগ্রাম আর এক পা ডাকা বাইনদা কুমিল্লার বরাবর ওর বিচি দুইটা জুলাইয়া পাশের রাষ্ট্র নোয়াখালী থেকে দৌড়ে এসে ওর বিচি বরাবর ডিল মারা উচিৎত এই শালায় নাকি নায়ক হাহাহাহাহা,1,"Meme, TikTok and others"
সাকা রে ফাঁকা বানাই ফেলছে কুকুরের কথা শুনলেই গাঁ জল্র,1,"Meme, TikTok and others"
চুদমারানী বালের নিউস,1,"Meme, TikTok and others"
খানকির পোলা তরে জন্ম দিয়া ভূল করছেতর মত বেজন্মা সন্তান রাস্তায় কুওার মত দাপরাইয়া মইরা জাওন দরকার,1,"Meme, TikTok and others"
কাকু হাগল,1,"Meme, TikTok and others"
ওকে কুততা দি য়ে মারো,1,"Meme, TikTok and others"
কুলাংগার সন্তান,1,"Meme, TikTok and others"
তুই মাদারচুদের কি অবস্থা হয় অপেক্ষায় থাক,1,"Meme, TikTok and others"
পূর্ণিমা অাপু হ্লারপুতরে ভালোই হেরেসমেন্ট করছে ৷,1,"Meme, TikTok and others"
একে জুতা পেটা করা দরকার শালা সুপার স্টার চুদাও সুপার স্টার এর স হবার যোগ্যতা আছে তর বাইনচুদ,1,"Meme, TikTok and others"
এই শালার পুতেরে জবাই কর,1,"Meme, TikTok and others"
এই সয়তন টকে ফাঁসি দেয়া উচিত,1,"Meme, TikTok and others"
ছেলে নামে জানোয়ার,1,"Meme, TikTok and others"
আমি সত্য বলছি যারা এই খবরগুলো বিশ্বাস করে তাদের মত বোকাচোদা আমি জীবনেও দেখিনি,1,"Meme, TikTok and others"
খানকী মাগী বেশা মাগী তরে ঘোড়া দিয়া এক পিট দিমু তুই কতটাকা নিবি,1,"Meme, TikTok and others"
খানকির পোলারে যদি পাইতাম মেরে ফেলতাম,1,"Meme, TikTok and others"
কুত্তার বাচ্চারে জুতা বাই রানের কাম,1,"Meme, TikTok and others"
এই জানুয়ারের বাচ্চার বিচার কি হবেনা এই এলাকাতে কোন পুরুষ নেই সবাই সন্তানের ভয়ে ভিতু এই হারামির বাচ্চাকে পুলিশের হাতে দেওয়ার দরকার কিপাবলিক বিচার করে ফেল্লে তো শেষ হয়ে যায়তার দুইটি হাত ভেঙ্গে গুড়িয়ে দেখ,1,"Meme, TikTok and others"
মোদির দুই গালে জুতা মারো তালে তালে পাকিস্তান জিন্দাবাদ,1,"Meme, TikTok and others"
কুততার বাচ্চা দুইটা রে খমতা দিলো কে,1,"Meme, TikTok and others"
শাস্তি চাইএই জানয়ার এরআমি লোকাল পুলিসকে অনুরোধ জানাই এই জানোয়ার কে গ্রেফতার এর জন্য,1,"Meme, TikTok and others"
পাচায় দিয়ে করতে দিবাচুষে দিবা,1,"Meme, TikTok and others"
আমি তসলিমা নাসরিন এর সাথে সেক্স করতে চাই জানি না আমার ওনাকে ভালো লাগবে কিনা তবে এটা বলতে পারি যে আমি ওনাকে আমার বেস্ট সেক্স দিব যেটা ওনার সারা জীবন মনে থাকবে আর আমার সাথে ছাড়া অন্য কোনো পুরুষের সাথে সেক্স করতে চাই বে না কথা দিলাম জানি না আমার এই কমেন্টটা ওনার কাছে পৌঁছবে কি না তবে তার জন্য আমি সারা জীবন অপেক্ষা করতে রাজি যদি কেউ ওনাকে আমার এই লেখাটা পোস্ট করতে পারেন তবে আমি তার জন্য সারা জীবন কৃতজ্ঞতা প্রকাশ করবো আমার ফোন নাম্বার এটা আমার অনেক দিনের স্বপ্ন অপেক্ষার অবসান চাই,1,"Meme, TikTok and others"
আঁখি আলমগীর একটা ফুন মোটা মাগী,1,"Meme, TikTok and others"
খানকি মাগি মিথিলা,1,"Meme, TikTok and others"
স্যাৎ চামড়ার মহিলাটিকে দেখলে মেজাজ গরম হয়ে যাই ফালতু মহিলা,1,"Meme, TikTok and others"
শালার দুইহাত কাটাহক,1,"Meme, TikTok and others"
বাংলাদেশে পাঠাবে মদি কে পুটকি মেরে মাইরালাব বাঙালিরা,1,"Meme, TikTok and others"
তুমারে বিস হাজার দিমু অইব নি গন্টা,1,"Meme, TikTok and others"
বেজন্মাশুয়োরের বাচ্চা গলায় পারা দিয়ে মেরে ফেলা উচিৎ,1,"Meme, TikTok and others"
সুয়ৌরের বাচ্ছাদের সুয়োরের মতো খবর৷ মোদী মোদী,1,"Meme, TikTok and others"
সালি চুতিয়া ভালো মানুষর খারাপ বলে,1,"Meme, TikTok and others"
কুকুরের বাচ্চার ফাসি চাই,1,"Meme, TikTok and others"
সালা কুত্তার বাচ্চারে দইরা মাইরালা,1,"Meme, TikTok and others"
পাশি চাই হারামযাদার,1,"Meme, TikTok and others"
শহীদ সালাউদ্দিন কাদেরকে রাজাকার বলার আগে হাসিনার মেয়ে পুতুলের শশুর ও দাদা শশুর কে যুদ্ধাপরাধী বল সালার ভারতের কুকুরের দল,1,"Meme, TikTok and others"
মার মার মারতেই থাক এইটা বাপ নামের কলংক এইসব কুত্তার জাত বাবাকে প্রতিটা দিন শুরু হোক আরো জঘন্যভাবে মেরে আমরা আছি ছেলের পক্ষে দাদা প্রদিপ সাহস হারিও না তোমাকে সালাম বা প্রনাম ভগবান তোমার মঙ্গল করবেই আর আদরের বৌটাকে কষ্ট দিও না বৌ এর মতো আপন আর কে আছে দাদা প্রদীপ তোমার বৌটা খুব বেশি লক্ষী তাকে সারাদিন রাখবে আদরে আদরে মা লক্ষী তোমার ঘর কখনও ছাড়বে না মাকেও মারতে হবে সুযোগ পেলেই মাকে মারলে তোমার লক্ষী বৌ সোনা খুশি হবে মা লক্ষী তোমার মংগল করবেই,1,"Meme, TikTok and others"
মাদারীরপু দেশে আয় একবার তোরে কুত্তা দিয়া তোরে পাছা মারামু,1,"Meme, TikTok and others"
মানুষ এমন জানয়ার হইতে পারে দেখে অবাক হলাম৷ বাবা মা হল প্রিথিবির সব চেয়ে বড় সম্পদ আর এই বাবা মাকে মানুষ কিভাবে কস্ট দেয় মানুষ দিন দিন জানয়ার হয়ে জাচ্ছে এইগুলা কেয়ামত এর আলামত ভিডিও দেখে আমার চোখে পানি এসে পরলো এই জানয়ারকে আমি পেলে খুন করতাম,1,"Meme, TikTok and others"
শালার কবিতা টা সুন্দর আছে মদ খাও আর শেখ হাসিনাকে চোদো,1,"Meme, TikTok and others"
শালির ঘরে শালি সব ভুয়া কথা বলে মানুষকে ঠকানো তোকে সামনে পাইলে জুতা পিটা করতাম,1,"Meme, TikTok and others"
জানোয়ার কে শরিলের চামরা তুলে তার পর লবন আর মরিচ গুঁড়ো মেখে দেওয়া হোক তার পর ও বুঝতে পারবে বাবা মাকে কি কষ্ট দিয়েছে,1,"Meme, TikTok and others"
এই সালাকে রাম কেলানী দেন সবাই জানোয়ার,1,"Meme, TikTok and others"
সামনে পেলে এই কুলাঙ্গারকে দেখিয়ে দিতাম,1,"Meme, TikTok and others"
বাগদাদের মত ফুটে যাবি শুয়োরের বাচ্চা মুসলমানরা,1,"Meme, TikTok and others"
ঐ কুত্তা একি কথা বলছ,1,"Meme, TikTok and others"
খানকি তোদেরকে হাত পা বেধে দোন দিয়ে চোদার চাইতো তোমার ভোদার মধে পা দিয়ে চোদাই মজা পাবে কারন হাত দিয়ে তোদের কিচু হবে না,1,"Meme, TikTok and others"
সব ওই খানকি মাগি বউ এর কাজ,1,"Meme, TikTok and others"
এতো দিন ছিল মা পাগল টাকার জন্য মেয়ে সাথী রায় পাগল খানকী,1,"Meme, TikTok and others"
এই কুকুর তুই নামাজ নিয়া খারাপ কথা বলিস না তা না হলে তোর জিব্বা টান দিয়া নিয়া আইসা কুত্তার ধনের লগে বেঁধে রাখমু,1,"Meme, TikTok and others"
ওরে চোদার দরকার,1,"Meme, TikTok and others"
এইটা যে জারজ সন্তান বুঝতে কারো বাকি না জারজ ছাড়া এই রকম কথা কে বলবো আর,1,"Meme, TikTok and others"
ফাটাকেষ্ট মারদে শালাকে,1,"Meme, TikTok and others"
এই কুত্তার গায়ের চামড়া তুলে ফেলতে হবে,1,"Meme, TikTok and others"
এই কুলাঙ্গার আর তার বউরে কচি বাশ দিয়ে পিটিয়ে পিটিয়ে লাল করে কালো করা উচিত,1,"Meme, TikTok and others"
এই হালার পু হালারে ফাসি দেওয়া উছিত,1,"Meme, TikTok and others"
মাংগের পোলা নামাজ নিয়ে গালি দিবি না,1,"Meme, TikTok and others"
তোদের কাছে আর কোন কাজ নাই সালারা,1,"Meme, TikTok and others"
রানু আর কি বুঝবে ওতো একটা পাগল বরং রানু বলতে পারে অতীন্দ্র ভগবান,1,"Meme, TikTok and others"
এই ধরনের সন্তান কে মেরে ফেলা উচিত,1,"Meme, TikTok and others"
তাহলে তোর স্তন টা দেখা আমি তাকিয়ে থাকি কিছুক্ষন,1,"Meme, TikTok and others"
এই মাগি তুই কোন জেলার মাইয়া,1,"Meme, TikTok and others"
সালার বেটারে ফাসি দেয়া হোক,1,"Meme, TikTok and others"
তোদের মতো জানোয়ার কে সামনে পেলে রে কেটে লবন দিতাম সালা জানোয়ার,1,"Meme, TikTok and others"
জারজ সাকা ওওর কবরে মুইত্তা আমু সালা জারজ ভাবছে ওওরে কেও ফাসি দিতে পারবে না,1,"Meme, TikTok and others"
শালি তোর এই খবর পড়া শুনলে মনে হয় দু গালে আচ্ছা করে থাবরাই দিই খানকি মাগি,1,"Meme, TikTok and others"
এই কুত্তাকে গুলি করে মার,1,"Meme, TikTok and others"
তুই মাগিরে আমি চুদিনা কারন তুই লক্ষ লক্ষ মানুযকে চুদাইছিচ,1,"Meme, TikTok and others"
তোমার টা কত ইন্ছি,1,"Meme, TikTok and others"
এই জানোয়ারকে এমন ভাবে পিটানো হোক যেন বাংলাদেশের সব মানুষ কখন আর বাবা মার প্রতি অসম্মান না করে,1,"Meme, TikTok and others"
ঐ মাদাৃ চোদ খানকির পোলা তর মায় রে চুইদ্দা মাল বাইর কইরা দিমু,1,"Meme, TikTok and others"
ওরে খানকির পোলাতোরে খুন করা উচিৎ,1,"Meme, TikTok and others"
হালার মুল্লারা ওয়াজে এগুলা কয় না কেলা,1,"Meme, TikTok and others"
তোরে জুতা মারমু,1,"Meme, TikTok and others"
এদেকে সেদ্দ গরম ডিম থ্যেরাপি দেয়া দরকার,1,"Meme, TikTok and others"
এইসব জানোয়ারদের মেরে ফেলতে ইচ্ছে করছে,1,"Meme, TikTok and others"
শুয়োরের বাচ্চারে মাইরা ফেলা উচিত,1,"Meme, TikTok and others"
তুমি এক রাতে জন্য এসো এমন চুদা চুদবো খুব মজা পাবে,1,"Meme, TikTok and others"
লোকটাকে যত গুলো থাপ্পড় দিলো তা বুকে এসে লাগল,1,"Meme, TikTok and others"
এই কুত্তার বাচ্চা না জন্মালে ও চলতো,1,"Meme, TikTok and others"
শালা পুরাই আবালচুদাবোকাচুদা,1,"Meme, TikTok and others"
তাই আমি জবার সিলেটে নাটক সব সময় দেখি বুঝছেন কিন্তু একটা কথা কি ভাই জানেন জবা কিন্তু ভাই মাল হিসাবে সে একটা জিনিস ওর দুধগুলো অনেক বড় বড়,1,"Meme, TikTok and others"
তুই কুকুরের চেয়েও অধম তর কি যোগ্যতা আছে যে তুই এইতা আজাইরা পাগলামি কথা কস তুই ত হালা জীবনে কিছুই করতে পারছস নাআবার এনে আইছস তর কুত্তার চেহেরা দেখাইতে কোথাকার,1,"Meme, TikTok and others"
তার বউটি কিছুই বলছে না কত খারাপ বউরে বাপ শালা কত খারাপ,1,"Meme, TikTok and others"
তোমার পুটকি দিয়ে চুদবোকতো নিবা,1,"Meme, TikTok and others"
এরকম ছেলে কে কুপিয়ে মারা উচাত,1,"Meme, TikTok and others"
এমন মেয়েদের কেন মিডিয়াতে ডাকা হয় এদের জন্য পতিতলায় ওকে,1,"Meme, TikTok and others"
এই শুওরের বাচ্চাকে ফাসি দেওয়া দরকার,1,"Meme, TikTok and others"
কুকুরের চেয়েও ূখারাপ,1,"Meme, TikTok and others"
এ কুতার বাচ্চা এটা তো অপু ছবি না,1,"Meme, TikTok and others"
মুদির বেশি আর সময় নাই সালার মালাউনের বাচ্চা রা তোদের বংশধর শুয়োরের,1,"Meme, TikTok and others"
জিনিসটা দেখার পর আমি অনেক অনেক কাদছি গত মাস আগে দেখছি এরকম সন্তান কারো ঘরে যেনো না জন্মায় অনেকক্ষণ মারার পর মনে হয় নিজের শক্তি হচ্ছিলো না এভাবে সন্তান মারলো সে মাথা নিচু করে চলে গেলো আল্লাহ এসব কুলাঙ্গার সন্তানদের কেন চোখে না,1,"Meme, TikTok and others"
সালি মিথ্যা কছ তরে চৌদি,1,"Meme, TikTok and others"
শালা মাদার চুত তুই,1,"Meme, TikTok and others"
তুই একটা বেস্সা মাঘী টাকার জন্য দেহ বিক্রি করছমাঘী,1,"Meme, TikTok and others"
রস আসলে চুদতে দিও,1,"Meme, TikTok and others"
হালাইতো পাগল শালা নাস্তিকের বাচ্চা,1,"Meme, TikTok and others"
জুতা পিটা করো রানুকে,1,"Meme, TikTok and others"
এই ধার্মিক মোল্লা শালারা ধর্মীয় জ্ঞান দিতে আসে কেনো সব জায়গায় এই শালাদের জন্যই দেশের আর্ট কালচার শিল্প সংগীত ধ্বংসের দিকে আজ অন্যদিনে হুহু করে বাড়ছে জেহাদি মানসিকতা নিজেদের মাথায় তো গু ভরা ভাল করে কোরান হাদিস পড়ে দেখ সব ভূলে ভরা মুহাম্মদ এর বানি এসব দিয়ে জীবন চালানোর কি আছে সব যে ভূয়া সেটা বুঝতে তোদের আরো কত যুগ লাগবে যারা বোঝে তারা তো আবার কথা বলতে পারে না কল্লা হারানোর ভয়ে,1,"Meme, TikTok and others"
এই ধরণের খানকি মাগীদের সালাম দেওয়া ঠিক হয়নি মাগীর এত সুন্দর চেহেরা কিন্তু পতিতা হয়েছে হায় কপাল,1,"Meme, TikTok and others"
এই শুয়োরের বাচ্চা,1,"Meme, TikTok and others"
তর উপর ঠাডা পরুক,1,"Meme, TikTok and others"
শালাক ল্যাংটা করে লাঠি দিয়ে পিটিয়ে হাত পা ভেঙ্গে দেওয়া হোক,1,"Meme, TikTok and others"
মাদার চোদ তকে যদি পাইতাম,1,"Meme, TikTok and others"
মোদি পাগল,1,"Meme, TikTok and others"
এই শালী তোমার ভোদা দিয়া কলা দিওয়া উচিত,1,"Meme, TikTok and others"
বোকাচোদাকে হাত দুটো কেটে দিকছিঃ৷ খুবি কষ্ট লাগল এমনটা কোন ছেলে করতে পারে তে ভিডিও টা যখন দেখি তাকাতেই পারছিলাম না উপযুক্ত সাজা পাক জানোয়ারটা,1,"Meme, TikTok and others"
এত খারাপ মানুষওকে ডিম থেরাপি দিতে হবে,1,"Meme, TikTok and others"
ও মানুষ না অমানুষ হায়রে দুনিয়া চোখের পানি ধরে রাখতে পারলাম না,1,"Meme, TikTok and others"
কুত্তারে পাশি দেয়া উচিত,1,"Meme, TikTok and others"
দাদা শালাকে আগে কেলাও মা বাবার অবিসাফ ধংস হোয়ে যাবে,1,"Meme, TikTok and others"
এই গাধার দল ওখানে রাম মন্দির ছিল আগে আলোচোনা হোক রাম মন্দির কেন ভাঙা হয়েছিল যে বলবির মুসলমান হয়েছে তার আহলে গরু খাওয়ার লোব জেগেছে মুসলমানদের আল্লা হচ্ছে হিন্দুদের শিব এটা প্রমানিত শত্ত আফগানিস্থানের নাম ছিল কুশশথলি জার রাজা ছিল রামের ছেলে কুশ,1,"Meme, TikTok and others"
মিন্নি মাগী নাম্বার খুনিএই ব্যাশ্যা কে নেংটা করে সারা দেশে ঘুরানো হওকনাহলে এই খানকীপতিতা কে কুত্তা দিয়ে চোদানো হওক,1,"Meme, TikTok and others"
মাদারচোদকে ফাসি দেয়া দ্কার,1,"Meme, TikTok and others"
বালের নায়ক তুই,1,"Meme, TikTok and others"
হের ভিডিও তে যারা লাইক দিসসতোগো মা গরে হেই চুদছিল তাই না,1,"Meme, TikTok and others"
তোমাদের মত মিডিয়াকে না জুতা খাওয়ায় দেওয়া দরকার বাদ দিয়ে দিবা এসব ফালতু জুতো দিয়ে মারতে মারতে মেরে ফেলবো,1,"Meme, TikTok and others"
এই মেয়ে টা জানি আরো কত ছেলের সাথে সম্পর্ক রয়েছে তা শুধু এই বেশ্যা মেয়েটাই জানে ৷৷ আর বিয়ে করলো তার বাবার সমতুল্য এক ছেলে কে,1,"Meme, TikTok and others"
শাস্তি চাই এই কুলাঙ্গার সন্তানের,1,"Meme, TikTok and others"
তোর গুষ্টিসহ চুদবো খানকির পোলা,1,"Meme, TikTok and others"
দেখলিই খেচতে মন হয়,1,"Meme, TikTok and others"
খানকি,1,"Meme, TikTok and others"
আমার বাড়ি বাংলাদেশ বিভাগ সিলেট সালা রে জুদি আমি পাইতাম তাহলে একটা ফায়ার দি মারতাম,1,"Meme, TikTok and others"
বালের রানু মন্ডল,1,"Meme, TikTok and others"
তোমার ভোদার সাইচ কত,1,"Meme, TikTok and others"
মাদারচোদ খবর এমন ডিস্ক্রিপশন অমন কেন,1,"Meme, TikTok and others"
তর মার চুদি,1,"Meme, TikTok and others"
হায়রে অভাগা বৃদ্ধ বাবা মাএরা সন্তান নাকি জানোয়ার,1,"Meme, TikTok and others"
চৈতালি বাল কেটেছো তো তোমার দুধ কতো বড়ো,1,"Meme, TikTok and others"
ওই মালটাকে ল্যাংটা করে ঝুলিয়ে পেছনে গড়ম মিষ্টি ঢেকাতে হয়,1,"Meme, TikTok and others"
ভারত মোদিকে জুতামারা দরকার কুকুরকে বাইচ্চা,1,"Meme, TikTok and others"
মাদরচুদরে এখন কবরে শয়তানে পুটকি মারতেছে,1,"Meme, TikTok and others"
মোদি কুওা নিপাত যাক পাকিস্তান জিন্দাবাদ,1,"Meme, TikTok and others"
খানকির পোলা নামাজ নিয়ে কিছু বলবি না,1,"Meme, TikTok and others"
এই জানোয়ারের অ্যাড্রেস কেউ দিতে পারবেন,1,"Meme, TikTok and others"
এই বানচোত এর সাথে ভালো কথা বলে লাভ নেইবানাতে হবে মাল টাকে,1,"Meme, TikTok and others"
সালা পোলা নামাজ কি করছে শেখ নামজের উপোর জিত কইরা নামাজ কে বক্কা দাও নামাজের বা ধরমীয় বিষে তুমি কথা বললে তোমার জিব্বা কসাইদের লোহার মাংসো জুলানো পেরাক দিয়া তোমার জিব্বা টানদিয়া গোড়াতে জিব্বা কাইটা দেবো কথাটা মন রাইখা কথা টা মনেরাখবি তোমার কথা শুনার কারন হলো তুমি জোকার চাল্লি তাই মানুষ কমিটির জন্য তোমার বিডিও দেখে,1,"Meme, TikTok and others"
কূটনীতি চালক ওই শালিকে জবাই করা হোক,1,"Meme, TikTok and others"
এই সালাকে সবার সামনে সাছতি দেয়া হক,1,"Meme, TikTok and others"
কিছু কিছু চেনেল আছে খানকির ছেলেদের কাজ,1,"Meme, TikTok and others"
গুড মারানী তোর কথার মধ্যে অনেক ফালতু কথা আছে এর পর থেকে সাবধানে রিপোর্ট তৈরি করবি,1,"Meme, TikTok and others"
পুরনিমার গুদে গন্ধো,1,"Meme, TikTok and others"
ময়ূরীর আমরার বিচি চোষার অভ্যাস,1,"Meme, TikTok and others"
এই কুত্তাটা যেন মারা যায়,1,"Meme, TikTok and others"
তোকে মাগি,1,"Meme, TikTok and others"
এই জানোয়ার কে ধরে মারা উচিত,1,"Meme, TikTok and others"
ভারতের মায়েরে চুদি,1,"Meme, TikTok and others"
তাহলে হিন্দুস্তানি সীমান্তরক্ষী বাহিনী বিএসএফের গুলিতে বাংলাদেশী নাগরিকদের নিহত হলো তাহলে বাংলাদেশের সীমান্তরক্ষী বাহিনী তথাকথিত বিজেপি তাহলে কি করে তারা কি বসে বসে কি ধন চুষে তারা কি বসে বসে ধোন চুষে ধন তারা শুধু বসে বসে ধোন চুষতে পারবে হিন্দুস্তানের করতে গিয়ে আজ হিন্দুস্থানের সীমান্তরক্ষী বাহিনী বিএসএফের গুলিতে বাঙালির নাগরিক নিহত হয় এর চাইতে আর দুঃখজনক এর চাইতে আর কি হতে পারে তাহলে বাঙালি সীমান্তরক্ষী বাহিনী তথাকথিত বাহিনী তারা মনে হয় বসে বসে ধোন চুষে তাদের আর কোন কিছু করার নেই,1,"Meme, TikTok and others"
ওই জানোয়ার টাকে ফাসি দেওয়া দরকার,1,"Meme, TikTok and others"
তোর গুদে গুলি সারা বিশ্বে মুসলিম জঙ্গি সংগঠন শেষ হচ্ছে আরো হবে সালা মুসলিমরা সব জঙ্গি,1,"Meme, TikTok and others"
শালার বাচ্চা দোয়া করি যে হাত দিয়ে মারলি ওই হাত তর পচেঁ পরবে,1,"Meme, TikTok and others"
বুবলি তুই একটা ডায়নি,1,"Meme, TikTok and others"
মহিলা কে চুদার দরকার,1,"Meme, TikTok and others"
তর মেয়েক খাব দিবি খেতে খানিকর পোলা,1,"Meme, TikTok and others"
ওই বাইনচুদ বাবাকে,1,"Meme, TikTok and others"
বোকাচোদাকে ঝুলিয়ে মারা উচিত,1,"Meme, TikTok and others"
সালা কুত্তার ছেয়ে ও অধম,1,"Meme, TikTok and others"
সব মাদারচোদ ইহুধির দালাল বাবরি মসজিদ ভাংলে মন্ধির ভাংতে হবে,1,"Meme, TikTok and others"
সালাকে আগে গন পিটুনি দেওয়া দরকার ছিলকারন সালা বলেছে রাগের মাথায় মেরেছে রাগের মাথায় কি এত গুলো মেরেছে এই সালার সাথে তার স্ত্রীকে ধরে নেওয়ার উচিত ছিল কারণ ওর স্ত্রী তো সামনে ছিল আমি মনে করি এই সালার চেয়ে তার স্ত্রী বেশি খারাপ না হলে এতগুলো চড় থাপ্পড় মারল এই মাগি আটকাতে পারল না,1,"Meme, TikTok and others"
আরে মাদারচোদ তুই পড়াশোনা শেষ কইরা রেশমির মতো হাজার পতিতালয়ের কনডম এবং প্যান্টি দুবি শালা,1,"Meme, TikTok and others"
কুওার বাচ্চা যে বাবা তোকে জন্ম দিয়ে তুই সেই বাবাকে চর মারলি,1,"Meme, TikTok and others"
সালা কে ওখানে ফাঁসি দেওয়া উচিত,1,"Meme, TikTok and others"
বুবলি একটা নস্টা মাগী অসামাজিক কুত্তার বাচ্ছা এই মেয়েটির কারনে আমাদের রাণীর এত কিছু গটতেছে,1,"Meme, TikTok and others"
তর বুধা ফাক কইরা দিমু,1,"Meme, TikTok and others"
চুদির ভাই,1,"Meme, TikTok and others"
হায়রে কুলাঙ্গার সন্তান ইস সয্য করা যায়না আব্বা কে হারিয়েছি অনেক আগেই আম্মু চোখের আড়াল হলেই একটুও ভালো থাকতে পারিনা,1,"Meme, TikTok and others"
এই শয়তান মহিলা কে জুতা মারুন মিথ্যা কথা বলে এই মহিলা,1,"Meme, TikTok and others"
তোর মতো মাগী টাকা দিয়ে চুদি মালায়েসিয়া,1,"Meme, TikTok and others"
হিন্দু সুনা পছন্দ ছিলো সেটা আগেই ডুকাতে পারতোসুধু সুধু একজনের জীবন কেনো নস্ট করলো মাগি খানকি,1,"Meme, TikTok and others"
তুই মদ কা কুত্তার বাচ্চা তুই তর মারে চুদ,1,"Meme, TikTok and others"
বাপ যেমন লুইচ্ছা মেয়ে ও তেমন লুইচ্ছি,1,"Meme, TikTok and others"
হে হল তার বাবার পাপে ফল শালা পাগল চোদা,1,"Meme, TikTok and others"
সালা শুধু লোকটাকে তুলে নিয়ে গেল কেনবৌটাকেও তোলা উচিত সামনে দাঁড়িয়ে মদত দিচ্ছে এইসব কুলাঙ্গার ছেলে বউ থাকার চেয়ে না থাকায় ভালো শিক্ষিত ছেলের কি কাজআবার বলছে রাগে করে ফেলেছিক্ষমা চেয়েছি সালা ওকেও ঐভাবে মারা উচিত,1,"Meme, TikTok and others"
দুদু দেখে ময়ু আনাট্রি,1,"Meme, TikTok and others"
এই জানোয়ার টারে আমি কাছে পাইলে আমি অই হাত ভেঙে ফেলতাম আর অর বউ মাগির ভুদার ভেতর কচু দিয়া ফাটাইতাম,1,"Meme, TikTok and others"
মাগী তোরা বাংলাদেশটা শেষ করে দিলি আর শালার মিডিয়াও হয়ে গেছে নির্লজ্জ,1,"Meme, TikTok and others"
মাদারচুদের বাচ্চারে পাইলে কিজে করতাম নিজেই জানি নাএগুলা কি মানুশ নাকি জানুয়ার,1,"Meme, TikTok and others"
খানকি মাগি বাংলাদেশি সঠিক নিউজ দেখা,1,"Meme, TikTok and others"
এই কুত্তা কে জুতা দিয়ে পৃথিবীর সমস্ত মানুষের সমস্ত জুতা দিয়ে ইচ্ছেমতো পিটানো দরকার বেয়াদব কুলাঙ্গার তোর সন্তানরা তোকে এমন মারবে দেখবি কুত্তা হাই ওয়ান জানোয়ার,1,"Meme, TikTok and others"
ওর গুয়া দিয়া পিচ শিদ্ধো ডিম দে,1,"Meme, TikTok and others"
কাকু খুব আকাম চুদাইচ জীবনে,1,"Meme, TikTok and others"
তোর মাকে সুয়োর দিয়ে দোদা মাগির ছেলে তোর মাাকে কয় যানোয়ারে চুদছে তুই এমন হইছিস কেনো তোর মাকেতো কোনো মানুষে চুদেনাই,1,"Meme, TikTok and others"
শালারে সামনে পেলে পিটিয়ে তার চামরা তুলতাম,1,"Meme, TikTok and others"
তোর দুধের সাইজ কত বল সালী,1,"Meme, TikTok and others"
মৌসুমি আর বুবলি এইটা পাগল আর ছাগল আর ফালতু অপু বিউটিফুল,1,"Meme, TikTok and others"
এই মাদার চোদ কে পিটাও,1,"Meme, TikTok and others"
তোরে মাইরা ফেলে না কেন আমি তোরে মারতে চাই তুরে মাইরা ফেলাবো আমি,1,"Meme, TikTok and others"
এই মাগির পোলার ফাঁসি চাই,1,"Meme, TikTok and others"
তুমি পপিও সেই সময় বহুজনকে চোদা দিছোতুমি আরো বড় যৌনকর্মি,1,"Meme, TikTok and others"
কুত্তার বাচ্চা কুলাঙ্গার সাকা,1,"Meme, TikTok and others"
সানাইয়ের মুখটা হইছে বইসা মাছের মত আর দুধ গুলা হচ্ছে ফুট কার মত,1,"Meme, TikTok and others"
তোর মতো আবাল চোদা একটা দেশের রাষ্ট্রপতি হলে সেই অবস্থা আর কত ভালো হতে পারে,1,"Meme, TikTok and others"
মদি কে মেরে ফেলা হোক,1,"Meme, TikTok and others"
সুচি মাগির ফাঁসি চাই,1,"Meme, TikTok and others"
সময় হলে বুঝবা তুমি ও একদিন বৃদ্ধ হবা শালার বউ,1,"Meme, TikTok and others"
এই সালার ছবিতে টু মারি দশকে তাকে কয়নি সুপার সে নিজে কয় যে আমি এক জন সুপার আগে করত অষ্টিল ছবি এখন আর কী এমন ভাল ছবি করের যে দশকে দেখত সিনেমা হলে গেলে দশক মিলেনা মিলে শুূদু মসা,1,"Meme, TikTok and others"
এই মাগির খবর এর সাথে মুখের মিল নাইতের বোদা পাটাবো,1,"Meme, TikTok and others"
ঐ মাদারচুদ বেব,1,"Meme, TikTok and others"
সালার ফুত কিদেখাছ,1,"Meme, TikTok and others"
ওই শালারে চোদা লাগবে শালা মানুষের বাচ্চা না,1,"Meme, TikTok and others"
শাল মানুষ না আওয়ামীলীগ,1,"Meme, TikTok and others"
এই বাইন চুদের ফাসি চাই তাও মাজ রাস্তাই জাতে সবাই জানতে পারে মানুষ রুপে পিচাস টা সাতে ওর বউ খানকি মাগির ও ওই মাগির বাচ্চা দারাই দারাই রং দেকছে খানকি মাগির গরে খানকি মাগি তর ভুদার ভিতর বেগুন মাগি ওদের ফাসি ফাসি ফাসি হক,1,"Meme, TikTok and others"
এই হালা একজন রাজাগার আর আহংকারী ছিলো তাই তাহার এরকম দশা হয়েছে,1,"Meme, TikTok and others"
এই তোর নাম কোন ধোনচোদায় রাখছে পুটকি চাট গরীব বাইঞ্চোদ,1,"Meme, TikTok and others"
ডানডির ঠেলা খায় নাছতিক,1,"Meme, TikTok and others"
ওই বেহায়ার বাচ্চা তুই জানিশ ফরিদপুরের মেয়েরা চোর এই তোর বাড়ী কোন জেলায়,1,"Meme, TikTok and others"
জানোয়ার এর যেনো সারা জীবন জেল হয়,1,"Meme, TikTok and others"
শাকিব তো কুকুর,1,"Meme, TikTok and others"
সালা নাসতিক,1,"Meme, TikTok and others"
কুলাঙ্গার ও কুলাঙ্গার রে তুই অপরাধী রে তোর বাবা তোকে জন্ম দিয়ে ভুল করছে রেতোর মতো ছেলেকে মেরে পেলা উচিত,1,"Meme, TikTok and others"
খানকি কে জুতা দেওয়া হক,1,"Meme, TikTok and others"
সালার গলার কন্ঠ মেয়েদের মতো,1,"Meme, TikTok and others"
এই পুলিশ কুত্তার বাচ্চা কে ভোহিস্কার করতে হবে এবং পুনররাই আবার জে এই পুলিশ কে চাকরী দেবে আমড়া ধোরে নিবো সে এক টা জারুজ সন্তান,1,"Meme, TikTok and others"
ওই কুকুর টাকে ফাঁসী দে,1,"Meme, TikTok and others"
এটা হিন্দুদের কালচার সালা অমানুষ,1,"Meme, TikTok and others"
নটি মাগি তুই জাকির নায়কে কি বলচি এত বাল মানুষ,1,"Meme, TikTok and others"
ভারতের মুদি বাবু কুত্তার বাচ্চা,1,"Meme, TikTok and others"
পতিতা মেয়েদের দালাল আমি সুমন ভাই,1,"Meme, TikTok and others"
শালা হারামিরে কুত্তা দিয়া খাওয়ান উচিৎ,1,"Meme, TikTok and others"
যারা রানু বারভাতারিকে করো না তারা একটা দিন,1,"Meme, TikTok and others"
এই কুত্তা কে জুতার মালা দিয়ে পুরো বাংলাদেশ ঘুরানো উচিৎ,1,"Meme, TikTok and others"
মদ খাও মাগি চুদ এটাতু বলেননি,1,"Meme, TikTok and others"
হেয় একটা ইবলিশ সয়তান হেয় ফেরাউন মোসলমান হতেই পারে নাতারে অনেক আগেই ঘৃণা করতাম কারন তার জে চরিত্র একজন মোসলমান এই রকম হতে পাড়ে না,1,"Meme, TikTok and others"
তোমার সোনার ভিডিও বানাইলা কেনো তোমাকে চোদার জন্য বেশ্যা শালী,1,"Meme, TikTok and others"
মোদী ও অমিত শাহ দুই কুকুর মেরে ফেললে তো সব ঠিক তাহলে এত মিটিং মিছিল এর দরকার না ওদের বাপের একা না দেশ টা,1,"Meme, TikTok and others"
মাগির পোত জার জন্য দুনিয়াতে আসচোত তাকে মারচ সালার পোত আমি জদি সামনে থাকতাম তোকে গুলি করে মারতাম,1,"Meme, TikTok and others"
খানকির ছেলে তর মায় কি বেসসা ছিল নাকি,1,"Meme, TikTok and others"
বুবলি একটা রেনড়ি মাগি অর ছবি দেখবোনা,1,"Meme, TikTok and others"
বাড়ার বাল তুই ই শুধু ফেক নিউজ বানাস শুধুমাত্র কিছু ভিউ পাওয়ার জন্য শালার ত্যালাপোকা কোথাকার চুদির ভাই,1,"Meme, TikTok and others"
সব হারামিরে মারন দরকার,1,"Meme, TikTok and others"
এই মাগির ফুয়া তুই নামায লইয়া গালি গালাজ করছ কেনে তর মারে ছুদি,1,"Meme, TikTok and others"
আবার ভিকারি অবস্তায় দেখতে চায় মাগিকে,1,"Meme, TikTok and others"
এই সয়তানের ব্চছা দের শিখা দেয়া উচিৎ,1,"Meme, TikTok and others"
জানোয়ারকে ফাসি দেওয়া উচিত,1,"Meme, TikTok and others"
তোকে কত জনে চুদে,1,"Meme, TikTok and others"
তোরে আমি পাইলে জুতা পিতা করতাম,1,"Meme, TikTok and others"
কুত্তার বাচ্চা ওরে পাইলে জবাই করে দিতাম ওর প্রত্যেকটি চরে ওর বাবা ওফ বলেছেন আমি দেখে কান্না ধরে রাখতে পারি নাই,1,"Meme, TikTok and others"
মানুষ হ জানুয়ারের বাচ্চা,1,"Meme, TikTok and others"
কুত্তার বাচ্চাকে পেলে পিটায়া পৃথিবী ছাড়া করতাম,1,"Meme, TikTok and others"
মডেল আরিফ খান আর এই হালাকে এক সাথে রাখলে আরিফ্ফা এই হালাকে পুটকি মেরে রেখে যাবে,1,"Meme, TikTok and others"
সালাক ফাসি দে,1,"Meme, TikTok and others"
নাস্তিক কুওার বাচ্চা,1,"Meme, TikTok and others"
হালায় মাগিদের দালাল,1,"Meme, TikTok and others"
মুসলার গুদ,1,"Meme, TikTok and others"
কি মিথিলা মালাওনের চুদা কেমন লাগে আর কয়দিন চলবে,1,"Meme, TikTok and others"
সালা মদি দেখ কেমন লাগে দেখ কেমন লাগবে,1,"Meme, TikTok and others"
কুলাংগারতোর হাত কেটে ফেলে উচিৎ,1,"Meme, TikTok and others"
সালার পুতেরে পাইলে কুপাইয়া মারতাম,1,"Meme, TikTok and others"
তুমার ভাই নাইনি আক্তা অ তারা দিএয়া সুদাউ না ক্নে বালা অইব,1,"Meme, TikTok and others"
মানুষ টা ভালবেসে স্ত্রীর মুখে একটা সন্দেশ বা মিষ্টি মুখে দিয়েছে আর কুলাংজ্ঞার টা কি করলো আর বাবা মার খেয়েও অভিযোগ করতে চাচ্ছেনা আদরের সন্তানের বিরুদ্ধে আহারে সন্তান আহারে মানুষ,1,"Meme, TikTok and others"
সালারে পাবনা পাঠা কেও তারাতারি,1,"Meme, TikTok and others"
খানকির ছেলে,1,"Meme, TikTok and others"
চুতমারানি খবর বন্দোকরো,1,"Meme, TikTok and others"
তোর মাসের ভোঁদা পাবে শালী,1,"Meme, TikTok and others"
মিনি খানিকির ফাসি চাই,1,"Meme, TikTok and others"
তুই নামাজ নিয়ে কটুকথা বলেচিশ আল্লাহ তোর মুখে কুস্টো ফেলুক জানোয়ার,1,"Meme, TikTok and others"
মদিকেএকহাজারজুতামারি,1,"Meme, TikTok and others"
খানকির পুলা তোর মারে চুদি,1,"Meme, TikTok and others"
রানী কাপড় খুইলা বস বেশি ভিউয়ার পাবি খানকিমাগী নটি,1,"Meme, TikTok and others"
তছলিমা গোড়ায় চোদে,1,"Meme, TikTok and others"
শুয়োরটাকে পেলে পিটিয়ে গায়ের ছাল তুলে দিতুম বাবার গায়ে হাত তোলে,1,"Meme, TikTok and others"
সালা বেটা ফালতু,1,"Meme, TikTok and others"
আল্লাহ ছারা কারো বিচার করার ক্ষমতা নাই এই পাপির এই  কুকুরের বাড়ি কোথায়,1,"Meme, TikTok and others"
সাকিবের বাল পালাইবি তুরা সাকিবের টাকার উপর লুভ পরেছে তুরার শালা কুত্তা ওগল,1,"Meme, TikTok and others"
আপু আপনার ব্রেষ্ট গুলোকি ঝুলে গেছে না টাইট খাড়া খাড়া আছে,1,"Meme, TikTok and others"
হালা খানকির পোলাতর বাবা তর মারে উল্টা কইরা চুইদ্দা তরে পয়দা করছিল,1,"Meme, TikTok and others"
খুব খুব খারাপ লাগলসময় টিভির কাছে আমার অনুরোধ হচ্ছে এটাকে বিশ্ববাসির কাছে তুলে ধরে ওই হারামির একটা উচিৎ শিক্ষা হওয়া দরকার,1,"Meme, TikTok and others"
মাদার চোদেরে পাইলে কোতাদে পুটকি মারালাম উলে,1,"Meme, TikTok and others"
আমার দশ মাসের একটা ছেলে আছে জানিনা আমার সাথে বড়ো হলে কি বেবোহার করবে,1,"Meme, TikTok and others"
একে মেরে পেল ভাই,1,"Meme, TikTok and others"
কয়টার সোনার চোদন খাইছো শালি রেশমি মাগি কুওা,1,"Meme, TikTok and others"
দেখে মনে হয় এই কুত্তার বাচ্চাকে কুত্তার মত পিটাই শালা,1,"Meme, TikTok and others"
শালারে মাইরা ফেলার দরকারনবির নামে উল্টা পাল্টা কথা বলেও হলো নম্বর মুরখো,1,"Meme, TikTok and others"
তোরে পাইলে কুপায় মারতামজারজের বাচ্চা,1,"Meme, TikTok and others"
বাপ্পিহিজ্রা তরে আমাগো শুশিল গ্রুপের লুইচ্চা টিকটিকি চুদে পতিতার গফ ভুদা খোর মাগি বাজ দের চুদা উচিৎ বাইঞ্চুদআবাল,1,"Meme, TikTok and others"
তুই নামাজ কে গালি দিছোস তোরে পাইলে তোর জিব্বা কেটে ফেলব,1,"Meme, TikTok and others"
তর মতন মেয়ে কারনে সকল মেয়ে খারাপ বলে মাগি,1,"Meme, TikTok and others"
এই কুত্তারে জবাই করে ফেলুক বাংলাদেশ সরকারে,1,"Meme, TikTok and others"
এই সালা বুয়া খবর দেয়ার জায়গা পাসনা,1,"Meme, TikTok and others"
মদি সালারে সব মুসলিম মিলে মারা দরকার মদি একটা কুততার বাচ্চা,1,"Meme, TikTok and others"
খানকির পুত তোর মারে চুদি খানকির পোলা,1,"Meme, TikTok and others"
ওই শুরের কি শাস্তি হয়েছেফাসি চাই ফাসি,1,"Meme, TikTok and others"
আমি তোরে পইলেঘোরা দিয়া গুয়া মারাইতাম,1,"Meme, TikTok and others"
নামাজের বিষয়ে কারাপ কথা বলবিনা তুই সুয়ারের বাচ্চা,1,"Meme, TikTok and others"
এই লোকের হাত দুইটি কেটে ফেলা হককি ভাবে বাবা সরিলে হাত উঠায় কঠিন বিচার করা হক,1,"Meme, TikTok and others"
তোরা দেখ দেখরে চাহিয়া বাপের পোলায় হাত তুলে কি বা কোরিয়া এ ছেলে নামে কলঙ্ক একে ফাঁসি দেওয়া উচিত এবং এটা থেকে আমাদের শিক্ষা নেয়া উচিত বাবা আমাদের জন্য তার জীবনের সব সুখ বিসর্জন দিয়ে আমাদের পেটের খাবার জোগানোর জন্য দিনরাত অক্লান্ত পরিশ্রম করে আমাদের সম্পূর্ণ চাহিদা মেটানোর চেষ্টা করেছে আর আর এই হারামজাদা সেই বাবার গায়ে হাত তুলেছে এর একটা হাত কেটে ফেলা উচিত আর পাশে যে বউটা শিখিয়ে দিচ্ছিল বউটাকে এক কোণে ডিব দিয়ে যাবজ্জীবন কারাদণ্ড দেওয়া উচিত,1,"Meme, TikTok and others"
এই রকম ছেলেকে আর ছেলের বউ কে একই গাছের সাথে পিটিয়ে ইচ্ছা মতো বারোতে হবে,1,"Meme, TikTok and others"
এই সালা ইয়াবা বেবসা করে উর বোউ নেসা করে,1,"Meme, TikTok and others"
বুবলির গুষ্টি চুদি,1,"Meme, TikTok and others"
এটা বাংলাদেশের হারামি মাগি ঢববাজ মিথ্যাবাদী,1,"Meme, TikTok and others"
ঐ কূত্তার বাচ্চা তুই মোহাম্মাদ নিয়ে গালি দিল ক‍্যান তুই বাংলাদেশ এ আসতোর ধোন কাইট্টা কুত্তা দিয়া খাওয়ামু,1,"Meme, TikTok and others"
সিফাত উল্লাহ একটা মাগির পুলা আপনারা কি বলেন,1,"Meme, TikTok and others"
নারী জাতি মার জাতি আমি তোমাদের কে পাইলে চুদি শান্তি দিতাম জারা নারিকে চুদি শান্তি দিতে পারে তারাই জননাত বাসিতাই তোদের চৌদ্দ গুসটির মারে বোন কে চুদি শান্তি দিতাম৷,1,"Meme, TikTok and others"
বাংলাদেশের পুলিশেরা পড়া কানকি মাগির পোলারা,1,"Meme, TikTok and others"
তোর মাকে তুই চুদ খানকিরপোলা তোর খানকি মাগির পোলা তোর মাইয়া ভিজিত টাকা তোর মাইয়া বুকেও এইডস আছে ভোদায়ও এইডস আছে তোর মায়ের পুটকিতে মাছের গন্ধ খানকিরপোলা চোদাচুদিতে ধনের পরিচয় তোর ধন আছে রে বাইঞ্চুদ তোর ধন খারায় যা ধন খারাইলে নিজের মায়রে চোদ খানকিরপোলা তোর মদ তোর হোগা দিয়া দিমু তোরে ফয়েল পেপারে ভহাইয়া তোর হোগায় আগুন দিমু খানকিরপোলা ছেছড়া চুদার বাল বেবলা চুদার বাল তোর ভুড়ির মদ্ধে কাউয়া হাগে তোরে হিজরা দিয়া চুদামু শালা বুইড়া লুইচ্ছা খানকিরপোলা,1,"Meme, TikTok and others"
এই কুত্তাটাকে খালি আমার সামনে এনে দাও কেউ ওকে মেরে দেওয়ার দায়িত্ব আমার এরপর আমার যা হওয়ার হবে আমি ফাঁসিতে ঝুলতেও রাজি আছি কুত্তা শালা,1,"Meme, TikTok and others"
কুত্তার বাচ্চাকে দুনিয়া থেকে তুলা দরকার,1,"Meme, TikTok and others"
এই জানুয়ার কে ফাশি দেওয়া হুক,1,"Meme, TikTok and others"
আমার নেতা,1,"Meme, TikTok and others"
দুধ দেইখা পাগল হইয়া গেলাম বাবারে বাবা দুধ,1,"Meme, TikTok and others"
তসলিমারে চুদমু,1,"Meme, TikTok and others"
খানকি মাগি তুই সিফাতের সাথে শুয়ে থাগ,1,"Meme, TikTok and others"
ওই বানচোদ কই থাকে ওরে পাইলে জুতা মারতাম,1,"Meme, TikTok and others"
আনলাইক দিছে কোন চোদানির পোলা,1,"Meme, TikTok and others"
এই কুলাঙ্গার জাহান্নাম সন্তানের ব্যাবহার দেখে আর সহ্য হচ্ছে না একে ধরে ফাঁসিতে ঝুলাও এই কুলাঙ্গার এর পৃথিবীতে বাঁচার অধিকার নেই,1,"Meme, TikTok and others"
এই মাগি তোর সাইয় কত,1,"Meme, TikTok and others"
তোর দুজনের মাকে চুদি খানকির পোলা বেজন্মা বেস্শা খানিক মাগী,1,"Meme, TikTok and others"
ঐ খানকির পূলা,1,"Meme, TikTok and others"
তুই মরার পর তরে চুদুম খাংকির পুলা,1,"Meme, TikTok and others"
মাগি বুবলি,1,"Meme, TikTok and others"
মাদারচুদ টাকু তর খবর করে ফেলব,1,"Meme, TikTok and others"
সালাকে পাচায় গরম ডিম ডুকে দেওয়া হউক,1,"Meme, TikTok and others"
এমাগি তুই প্রত্যেক দিনে কি খবর পড়িস এর থেকে আমাদের কাছে ভালো খবর আছে,1,"Meme, TikTok and others"
এরকম কুকুরের বাচ্চা যেন না জন্মায়,1,"Meme, TikTok and others"
মোদি ও অমিত মাদারচুদের ফাসি চাই,1,"Meme, TikTok and others"
ওভারএ্যাকটিং তোদের হোগা মারছে,1,"Meme, TikTok and others"
মাগির ছেলের আগুন দিয়ে মারা ইচিত কি বলেন ভাইরা সালা কুকুরির বাচা,1,"Meme, TikTok and others"
জানোয়ার কুত্তাকে উচিত শিক্ষা হিসেবে ওর হাত কেটে দেওয়া হোক,1,"Meme, TikTok and others"
বুবলি একটা মাগি,1,"Meme, TikTok and others"
এই যে ভাইয়ের তুমরা বলে যাও এই গাধা নায়ক কিভাবে হলো,1,"Meme, TikTok and others"
খানকী কি গায়ে লেখা থাকে চোদা জনের খাইয়া বিগোতে আসে,1,"Meme, TikTok and others"
আবার কত বড় সাহস্যা আবার বলে তুই বলে ওরে পিটাও মাগীর পোলারে,1,"Meme, TikTok and others"
তোজলিমা শালী একটা রেনডি,1,"Meme, TikTok and others"
মোদি শালাকে জুতা দিয়ে পিটাও তাইলে আর কোন দিন এইধরনের অপরাধ করবে না ইনশাআল্লাহ,1,"Meme, TikTok and others"
সালা বেয়াদব,1,"Meme, TikTok and others"
ভাই এর ঠিকানা দিন মাদার চোদের দুই হাত কেটে দেই আমাকে ফোন দিন আর এর ঠিকানা দিন,1,"Meme, TikTok and others"
একে জুতা মারো তালে তালে,1,"Meme, TikTok and others"
এই কুকুরকে ফাসি দেওয়া দরকার,1,"Meme, TikTok and others"
সাকিব খান সয়তান সালা এক টা গরু,1,"Meme, TikTok and others"
তোমারে চুদতে চাই ঘনটা কত টাকা,1,"Meme, TikTok and others"
শালা তুই একটা শুয়োরের বাচ্চা ইউটিউব চালাস কেন শালা বানচোদ আবার সেই সিফাত উল্লাহ কে মানুষের মাঝে নিয়ে আসছিস কুত্তার বাচ্চা মানুষের কাজে আসে আমার ভিডিও বানা এসব বালছাল ভিডিও দিস কেন,1,"Meme, TikTok and others"
এই মাগী বাংলাদেশ থেকে সোনাগাছিতে এসেছে চোদন খেয়ে পয়সা কামাতে শালি হালালার পয়দা,1,"Meme, TikTok and others"
সিফাত উল্লাহ তো ভালোই লাগে কিন্তু এ শালা বলে মুক্তিযোদ্ধা সোনার মুক্তিযুদ্ধে অস্ট্রেলিয়া বাংলাদেশ থেকে কোন কথা কইতে না কিয়ের ব্যবহার করে বাংলাদেশে ভুয়া মুক্তিযোদ্ধা ভুয়া মুক্তিযোদ্ধা মুক্তিযোদ্ধা,1,"Meme, TikTok and others"
কুত্তার বাচ্চা ভিডিও না করে ওকে আগে পিটাতি আগে,1,"Meme, TikTok and others"
বাইনচোদ রে কুত্তা দিয়া খাউয়ানো উচিত,1,"Meme, TikTok and others"
সালার পো ফাসি দেওয়া দরকার,1,"Meme, TikTok and others"
শালায় একটা মাদারচোদআল্লাহ অর সন্তান এর হাতে জেনো একি রকম ভাবে মাইর খাওয়ার তোওফিক দান করেন আমিন,1,"Meme, TikTok and others"
তুই গাজা খোর,1,"Meme, TikTok and others"
তুরে পাইলে কোন করতাম শালার পুত,1,"Meme, TikTok and others"
ও তোর মত ছেলে থাকার চেয়ে না থাকাই ভালো শালা একটা পশু,1,"Meme, TikTok and others"
মাদারচুদের বাচ্চাকে পাগলা কুকুরের সামনে বেঁধে রাখা দরকার,1,"Meme, TikTok and others"
খানকির পোলা তোর পোলা তোরে পিটাবে ন্যাংটা করে,1,"Meme, TikTok and others"
মোহাম্মদ সাঃ নিয়ে কিছু কইবি না মাদারচোদ,1,"Meme, TikTok and others"
আপু আপনার দুধুর সাইজ কত,1,"Meme, TikTok and others"
এই বউয়ের দালাল বউয়ের মুরিদ হইছে ওরে পুটকিমাইরা মাইরা লা,1,"Meme, TikTok and others"
ফ‌িগার বল‌ত‌ে কি দু‌ধের মাপ বোঝা‌চ্ছেন,1,"Meme, TikTok and others"
এই মাগির গুদে রাজা মরিছ ডুকান,1,"Meme, TikTok and others"
কুত্তার বাচ্চারে মাইরা ফেলা উচিত ছিল শুয়োরের বাচ্চা শুয়োর,1,"Meme, TikTok and others"
বালের নায়িকা অপু বিশ্বাস,1,"Meme, TikTok and others"
জানোয়ার তোর ছেলে তোকে মারবে,1,"Meme, TikTok and others"
মাগির পুটকি অনেক ভার ওকে চুদতে হবে,1,"Meme, TikTok and others"
পরকীয়া না করেই কি ডক্টররেট পেয়েছে আপনারা দেখবেন সৃজিত ভালোভাবে খেয়ে একলাথি মারবে ঠিক জালে গিয়ে বল পড়বে তখন দেখবে মজাটা আমরা এই টা দেখার জন্য বসেথাকব,1,"Meme, TikTok and others"
জুতা মারা দরকার কুওার বাচ্চাকে,1,"Meme, TikTok and others"
কিত্তার বাচ্চা,1,"Meme, TikTok and others"
খানকি একটা,1,"Meme, TikTok and others"
মাগির পোয়ারে পাসি দেওয়া উচিত,1,"Meme, TikTok and others"
ওকে এখন বানিয়ে রাখা হয়েছে কুত্তা কথাকার,1,"Meme, TikTok and others"
এই খান কির পোলা সিফাত উল্যা তুর মারে চুদি,1,"Meme, TikTok and others"
চোখের পানি আটকাতে অনেক চেষ্টা করেছি কিন্তু পারলাম না ওকে দুনিয়ার সবচেয়ে জঘন্য ভাবে নির্যাতন করে জনতার মাঝে প্রকাশ্যে পুরি ফেলা উচিত যাতে পৃথিবীতে ওর মতো আর কোন যানোয়ার জম্ম না হয়,1,"Meme, TikTok and others"
বাংলায় আচোদা বলে একটি কথা আছে এখানে ডাক্তার এবং উুপস্থাপিকা দুজনেই আচোদা কত বেয়াক্কেল ও নির্বোধ হইলে এই ধরনের প্রোগ্রাম করতে পারে তা আমার বোধগম্য নয় আচ্ছা এই প্রোগ্রাম তো এদের পরিবার নিকট আত্মিয় সবাই দেখবে এদের বিন্দুমাত্র লজ্জাবোধ ও নাই এদের শরীরে পোশাক মানায় না এদের উচিৎ উলঙ্গভাবে চলাফেরা করা,1,"Meme, TikTok and others"
মাদার চুদ তর মা কে চুদি,1,"Meme, TikTok and others"
এদের জন্মের ঠিক নেই,1,"Meme, TikTok and others"
সেফু তোর হেন্ডা চিড়ালামু তুই নামজরে গালি দিচস কেন ওরে কেউ দইরা সাউয়া চিড়ালা,1,"Meme, TikTok and others"
খানকি মাগি আর কোন খবর পাসনা,1,"Meme, TikTok and others"
সালিদের জন্য বাসায় টিভি দেখতে পারি না,1,"Meme, TikTok and others"
এই সালাতো থাপ্পর না জুতা দিয়ে মাইর খাবে তার নিজ সন্তান থেকে৷ সালা মরার সময় পানিও পাবে না,1,"Meme, TikTok and others"
তোর কুলাঙ্গারকে আমার সামনে পড়লে জুতা পেটা করতে জাহান্নামে পাঠাতাম,1,"Meme, TikTok and others"
সালা ঠিকানা জানলে অবশ্যয় জানাবেন,1,"Meme, TikTok and others"
এখানে কিছু ছাগলদের কমেন্ট পড়ছি বাংলাদেশে যে এখনো ছাগল আছে এখানে না আসলে বুঝা যেতন বেস্ট ক্যান্সার বা বেস্টের সমস্যা নিয়ে আলোচনা হতেই পারে এখানে ছি ছি করার কি আছে এর ফলে সচেতনতা বাড়াতেছে যা খুব দরকার,1,"Meme, TikTok and others"
মদিকেজুতামারিএখন,1,"Meme, TikTok and others"
সালা মাগীর বাচ্চা ওরে পেলে আমি,1,"Meme, TikTok and others"
এরে নায়ক বানাইছে কোন পাগলে,1,"Meme, TikTok and others"
কুত্তার বাচ্চা মিত্তা প্রচার কইরা কি হয় তোর,1,"Meme, TikTok and others"
এই কুততাটার ফাসি চাইদেওয়া হোক মিততুদনডোআর সকল প্রতিবেসিদের এরকম হওয়া উচিতওরে উচিত সিকখা দেওয়া হোক সরকার থেকেএরকম কুকুরকেজে বাবা জনমো দেই সেই বাবার সাথে এরকম আচরন,1,"Meme, TikTok and others"
কলকাতার সেক্সি মহিলা বা বিধবা সেক্সি বয়স্কা থাকলে এসওও আমার বয়স্কদের চুদতে দারুন লাগে এ ভিডিও কল করে চুদবো এসওওওও এসওওওও,1,"Meme, TikTok and others"
মাগী তোর বোদার মদ্যে চুলকানী বেসি তোরে চুদে চুদে তোর বোদা ফাটিয়ে ফেলবো আর যদি এমন খারাফ ভিডিও ছাড়বী,1,"Meme, TikTok and others"
ডাকতার আপা আপনার বেসটের সাইজ কত,1,"Meme, TikTok and others"
তর চৌদার দোষ ছিল,1,"Meme, TikTok and others"
কুত্তার বাচ্চারে জীবন্ত পুড়িয়ে মারেন সমাজে এমন কাজ যেন কেউ করার স্পর্ধা না দেখায়,1,"Meme, TikTok and others"
মুদি কি তোর ভাতার খবর গুলো পাস কথাই এই ধরনের খবর আর দিবিনা,1,"Meme, TikTok and others"
মাদার চোত কে ফাসির পর আগুন দিয়ে পুড়াই দিয়া উচিত ছিলো,1,"Meme, TikTok and others"
ওকে কুত্তা দিয়া চোদা উচিৎ ও একটা জানোয়ার লুচ্চামি করা ওর পেশা ওকে শুয়োরের মতো দেখতে,1,"Meme, TikTok and others"
এই মাগিরে বাংলা দেশে রাখাই উচিত না মাগি ওর মায়রে চুদ্দে হবে কেন এমন খুলাংগার মেয়ে জন্ম দিছে,1,"Meme, TikTok and others"
শালা পুরুষ নামের কলংক,1,"Meme, TikTok and others"
মাদারচোদ কুকুরের বাচ্ছা,1,"Meme, TikTok and others"
তোমাকে চুদব আস,1,"Meme, TikTok and others"
পূর্ণিমা বয়স হলে কি হবে মালটা সেক্সি নাম্বার ওয়ান পূর্নিমার হট গান দেখলে মাথা ঠিক থাকে না পূর্ণিমাকে যদি একবার পাইতাম সারা জীবন লাগাইতাম,1,"Meme, TikTok and others"
কুত্তার বাচ্চা তাকে কুপিয়ে আমি হত্যা করতামপৃথিবীর সবচেয়ে বড় আসামি থাকলে এই কুত্তার বাচ্চাই আছে,1,"Meme, TikTok and others"
এই খানকির পোলা সেফায়েত উল্লাহ মাদারচোদ জীবনে যদি তোরে একবার সামনে পাই তোর মারে তোর কাঁদের উপর রাইখা চুদমু মাদারি,1,"Meme, TikTok and others"
তোমার ভোদার ভিডিও আপলোড কর সবস্ক্রাইট করবো মাগি,1,"Meme, TikTok and others"
আহা ওরে শুয়োর বাবা মা কত কষ্ট করে তোরে মানুষ করেছে তুই ভুলে গেলি তবে তুই দেখিস তোর ছেলে একদিন তোরে এইভাবে পেটাবে অপেক্ষায় থাকলাম,1,"Meme, TikTok and others"
দেহ বিক্রি করা মাগিরা,1,"Meme, TikTok and others"
এই মাগি নিয়ে নতুন করে বলার কি আছে,1,"Meme, TikTok and others"
রানুর মে লুবি ওকে রানুর কাছে আসতে ছেনো না দেয়া বিকারি মাকে পরিচয় দিতে লজা লালো আজ মিডিআর পদায় দেখেমাকে দরোদ বেবে পরছে লুবি মে টাকা হাতাতে আসছে ওমার লাথি মেরে বের কোরে ধেক মিডিআর লোকেরা রানুর মেএকে জাদেখে কুলাগার ছেলে মে সিখা পয়া রানুর মেএর মুখে থুথু আর কুকুরের গু মাখি বজাত মে লাথিমেরে বের করে ধেক ছালমান খান আর হিমেস মিডিআ থেকে ওমেএকে বজাতমে ঐ ছেলে দুটো ভালো বলে ওকে কিছু বলোনা ওন্নকোনো ছেলে হলে ওকে ছিরে খেতো,1,"Meme, TikTok and others"
কুত্তার বাচ্চা তোরে পাইলে শেষ করে দেবো কুত্তার বাচ্চা,1,"Meme, TikTok and others"
দাবি আমার একটাই এই কুলাঙ্ঘারের ফাসি চাই,1,"Meme, TikTok and others"
এই হারামী টাকে মেরে ফেলে ওর মাংস কুত্তা দিয়ে খাওয়ানো হোক এই হারামীর ফাশি চাই,1,"Meme, TikTok and others"
মানূষ এত খারাপকুত্তাটা রে লেংটা করে মারা দরকার,1,"Meme, TikTok and others"
অরে বাপ্পী তুই একটা চুদিরভাই তুই একটা কুত্তা তুই একটা গাধা তরে নায়ক বানাই ছিল কেরে না তুই তো একটা নায়িকা,1,"Meme, TikTok and others"
এই কুওাকে ফাঁসি দেওয়া হক,1,"Meme, TikTok and others"
মাগীবেয়াদব মহিলা তােরনংদে,1,"Meme, TikTok and others"
শালারে ফাঁসিতে ঝুলান,1,"Meme, TikTok and others"
মুদি কে চুদি,1,"Meme, TikTok and others"
ঐ শালার স্ত্রীকে ও পুলিশে দেয়া উচিৎ ছিল,1,"Meme, TikTok and others"
কুত্তার বাচ্চা আজকে তোর গায়ে শক্তি আছে দেখে বাপকে মারছিস একদিন এমন দিন আসবে তোর ছেলে তোকে লাথি মারবে জানোয়ার,1,"Meme, TikTok and others"
এরকম কুকুরের ছেলে হবার কোন অধিকার নেই এর শাস্তি দেওয়া উচিৎ না হলে এই রকম কুকুরের পাওয়ার বেড়ে যাবে,1,"Meme, TikTok and others"
তাসলিমা মাগীরে কুত্তা দিয়া পুটকিমারা নো দরকার,1,"Meme, TikTok and others"
পরীমনি বাংলাদেশ চলচ্চিত্রের করলো জাজের সাথে তিনরাত চুদা খেয়ে ফলাফল জিএম ডাবলু গাড়িআর আমরা দিলাম ছবি দেখাবাদ,1,"Meme, TikTok and others"
বিশাল বিশাল দুধ গুলো কে খায় তোর ভোদায় হাতির ধোন ঢুকিয়ে রাখিস নাকি,1,"Meme, TikTok and others"
নোংরামি বোকাচোদা,1,"Meme, TikTok and others"
নরাধম অমিত শাহ অমিত শাহ সন্ত্রাসী মুসলিম বিদ্বেষী ও হীনমন্য হনুমান রাজ,1,"Meme, TikTok and others"
ওই ম তোরে লাগাতে দিবি একটু তুই তো অনেক সেক্সি রে নোয়াখাইল্লা মেয়েরা লুচ্চা বেশি বেশি লাগায় আমার কাছে তো মনে হয় তুই তোর বাড়ি নোয়াখালী তোর ভিজিট কত লাগে জানাইস খানকিমাগী,1,"Meme, TikTok and others"
ঔ শালার বৌ কে জেলে দেওয়ার দরকার,1,"Meme, TikTok and others"
এমন ছেলে কে কুপিয়ে হত্যা করা উচিত,1,"Meme, TikTok and others"
মাগী তুমি পরকীয়া কর তোমার জামায় না বলে স্বামী ছিছি,1,"Meme, TikTok and others"
উত্তর কোরিয়া তোর মায়ের বম ফেলবে মাদার চোদের খানকীর আম্মুর ছেলে,1,"Meme, TikTok and others"
মাগির ধুদ এতো বড় কেন,1,"Meme, TikTok and others"
মাদারচোদ তোর সোনা কাটমু,1,"Meme, TikTok and others"
মাদারচুদ তর মার বুদা দিয়া তরে ডুকায়া দিমু,1,"Meme, TikTok and others"
আপু তোমার নামবারটা দিবেন,1,"Meme, TikTok and others"
তুই নিজে বেশ্যা,1,"Meme, TikTok and others"
বাংলাদেশে বেশি হিন্দু রা এগুলো করে এদের ধরে জেলে দেন সালে মালাউন,1,"Meme, TikTok and others"
সালার বলদ,1,"Meme, TikTok and others"
মাগির ছামায় মনে হয় একজয় আস্ত মানুষ ডুকাইয়া চোদা যাইবে,1,"Meme, TikTok and others"
বোকাচোদাটাকে সামনে পেলে প্রচুর মার মারতাম খুব করে কেলাতে ইচ্ছে করছে,1,"Meme, TikTok and others"
মাগি তোমারে চুদতে চাই,1,"Meme, TikTok and others"
নস্টা তোর পোশাক এই বলিতেছে তুই ও মুদির আকাড়া লিংগ দুকেছে যে তোদের মতো নস্টাদের কারনে আজ কুরআন এর অসন্মান হচ্ছে,1,"Meme, TikTok and others"
কুকুর কে মোগর দিয়ে পিঠিয়ে কাসমিরকে আজাদ কর,1,"Meme, TikTok and others"
ভাই কেমনে বুঝব জিতের বউ ভাল এক বার চোদে দেখতে হবে ভাল না খারাব,1,"Meme, TikTok and others"
ময়ুরির দুধ দুইটারে কতো মানুষে টিপছে তাই এতো বড়ো দুধ,1,"Meme, TikTok and others"
বাইনচুদ তোর মুখে মুতি খানকির পুলা তুই ধর্ম নিয়া কথা বলিসতোর ঠিকানা তো জাহান্নামেও হবে না,1,"Meme, TikTok and others"
বাইন চোদদদদদদতোর ধোনের মধ্যে বাশ ডুকাবো,1,"Meme, TikTok and others"
খানিক মাগি তোর বিএনপি দালালী চোদাছ তোর মাকে চুদবো তোর বাবারে গলায় বেঁধে,1,"Meme, TikTok and others"
সালাহ উদ্দিন চৌধুরী একজন ভালো ব্যক্তি ছিলেন এখন যারা তার বিরোধি আসলে তারা রাজাকারের চোদায় জন্ম মাদার চোদেরা বিএনপির বিরুদ্ধতা করো শেখ মুজিব তো যুদ্ধ ঘোষনা দিয়ে দেশ ছেড়ে পাকিস্তানের কাছে আশ্রয় নিয়েছিলো আর জিয়াউর রহমান সেদিন যুদ্বের প্রস্তুতি না নিলে কখনোই এই দেশ সাদিনতার মুখ দেখতো না আজ যারা কুত্তালীগ করে আর বড় বড় কথা বলে তারা আসলে জারজ সন্তান কুত্তার বাচ্চার চাইতেও খারাপ কেননা তারা সত্যে সিকার করতে নারাজ এরা আসলে মাদার চোদ,1,"Meme, TikTok and others"
তর তো বাল চুল সব পেকে গেছে মাগী এখনো সময় আছে ভালো হয়ে যাআর কিছু সালা আছে পাগল,1,"Meme, TikTok and others"
ভারতের ষড়যন্ত্রের শিকার সাকিববাংলাদেশ ক্রিকেট কে ধ্বংস করার চক্রান্তধিক্কার ঘৃণা করি আইসিসি ও রেন্ডিয়াকেথুথুথু,0,sports
টিম ডংসো হইছে সাল থেকেওয়ার্ল্ড কাপে তার প্রমানআর আগের মতন হবে না বছরে ও ঠিক হবে নাকারন বাংলাদেশ টিমে নিউ নাই তার জন্য পুরুনো খেলয়ারযা মনে চায় তাই করতে পারেকথা হবে কিন্তু খেলা বন্দো করে,0,sports
এক এক যুগে বাংলাদেশ একেকটা হিরোকে ধ্বংস করছে,0,sports
নটির পোলা পাপন সব তোর খেলা,0,sports
বাংলাদেশের মানুষ সবাই গর্জে ওঠো পাপনের বিরুদ্ধেতা না হলে বাংলাদেশের ক্রিকেট কে ধ্বংস করবে পাপন সবাই আমার সাথে একমত,0,sports
কে সেৱা বাংলাদেশ টিমেৱ মাশৱাফি সাকিব,0,sports
এবার বিপিএল জমে উঠেছে,0,sports
"আমি মনে করি,বাংলাদেশ জাতীয় দলে খেলার অধিকার সাব্বির এর নেই........এই ধরনের খেলোয়ার এখন বাংলাদেশ জাতীয় দলে না থাকাটা ভালো...",0,sports
হুম প্রেসে বসে এমন পকপক সবাই করতে পারে। আপনি যদি পাপনের গদিতে থাকতেন তখন বুঝা যেত আপনি কেমন। সবাই এখানে আপনার প্রশংসা করে ফাটিয়ে দিছে কেননা আপনার কথাগুলি যৌক্তিক তবে কিছু কিছু অযৌক্তিকও ছিল। আর এমন ব্যাপার যেন পাপন বিসিবির জন্য কিসুই করেনি! আর খেলোয়াড়দের পক্ষেও একটু তেলবাজি করলেন। আমার কথা হল পাপন যে বল্ল কেন আমাকে একটিবারের জন্যও জানানে হল না? কেন আমাদের সাথে না বসে ধর্মঘট করল?? এটা কি প্লেয়াররা ভুল করেনি? কই একবারোতো বল্লেন না যে এজন্য প্লেয়ারদের ভুল স্বীকার করা উচিত!!বুঝি বুঝি সবই বুঝি। প্লেয়ারদের পক্ষে একটু তেলবাজি করলেন এতে করে পাপনের গদিটা যদি আপনি পান আরকি!!!😄😄,0,sports
সব কিছু মুক্তিযুদ্ধের নাম দিয়ে চলে না? মুক্তিযুদ্ধ হচ্ছে আমাদের অস্তিত্ব সেই অস্তিত্ব নিয়ে লিলা খেলা চলছে তার নায়ক আমাদের পাপন সাহেব। এখানে জুড় করে খেলোয়াড়দের উপর থেকে স্বাধীনতা কেড়ে নেওয়া হয়েছে,0,sports
সে না হয় নারী সঙ্গ পেতে ভালোবাসে <br />কিন্তু এই যে নারীরা।তারা কি তার সঙ্গ পেতে ভালোবাসে না,0,sports
রুবেল নামের ছেলেরা একদম ফাজিল হয় আমার চেনাজানা রুবেল নামের ছেলেরা ফাজিল এরে উচিত শিক্ষা দেওয়া উচিত ছিল,0,sports
পাপন সাহেব অনেক হয়েছে এখন আপনি বিরতি নেন,0,sports
ভাই খারাপ লাগাটা অনেক বেশি কাজ করতেছে সত্যি হ্রিদয়টা পুড়ে যাচ্ছে। আপনার জন্য অনেক ভালোবাসাসাকিব ভাই।,0,sports
আলহামদুলিল্লাহ খুব ভালো লাগল। কুমিল্লা ওয়ারিয়র্স দের কে স্বাগতম।,0,sports
এক তাহসিন আজ সারা বাংলা কাপাচ্ছে আলহামদুলিল্লাহ,0,sports
পাপনের জন্য আজ এই অবস্থা,0,sports
আফসোস্!😑আজও তাহসিনেশন ভাইয়াকে সাবস্ক্রাইবার উপহার দিতে পারলাম না😑😑,0,sports
আরে তুই হেডলাইন দিলি সে নিশ্চিত খেলবে এর কোনটাই খবরে দেখা গেলো না মিথ্যুক,0,sports
আমাদের ময়মনসিংহের অহংকার মাহমুদুল্লাহ,0,sports
খেলার সময় ছাগলদের বডি ল্যাংগুয়েজ বলে দেয় যে ওরা পিকনিকে গেছে।আগে ফুটবলে আমরা অনেক ভালো ছিলাম।আর বিনোদনের প্রধানক্ষেত্র এটাই ছিল।এটা মোটামুটি ধ্বংসের দ্বারপ্রান্তে চলে গিয়েছিল।এখন ক্রিকেটটাও ওই পর্যায়ে চলে যাচ্ছে মনে হয়।,0,sports
সাকিব অপরাধ না করেও শাস্তি পেলো।কিন্তু আগারওয়াল কে তার ব্যাপারে আইসিসি ও আকসু কি পদক্ষেপ নেয় এই বিষয়টা মিডিয়াকে খুজতে হবে,0,sports
নাইস খেলা,0,sports
বাংলাদেশে ক্রিকেট খেলা নিষিদ্ধ হওয়া দরকারউন্নত দেশের কি কোন ক্রিকেট টিম আছে ?,0,sports
মাশরাফির পরিবর্তে ইমরুল /মুমিন কে দলে চাই,0,sports
পাপন কাকু তোমার সময় ঘনিয়ে আসতেছে,0,sports
অাফগানিস্থানের সাথে পানি খায় অাবার ম শ্রেণীর ক্রিকেটে লাখ টাকা ম্যাচ ফি চায়,0,sports
রাজনীতি চুদাইলে ক্রিকেটের উন্নতি হবে কেমনে????,0,sports
তোমার জ্বলে কেন,0,sports
আমি আপনার কথাগুলোর সাথে সহমত আছি,0,sports
সাকিবের পাশে আছি সবসময়,0,sports
খেলা বন্ধ করা ঠিক হয় নাই আর কি বাল করবে করে রান তবুও কোটি টাকা,0,sports
কোন মিস করি বস তোমাকে😭,0,sports
ভাই তুমি বললে কিছু কি হবে,0,sports
এই কাজ টা করা টিক হয়নি,0,sports
তামিম ইকবল খান🥰🥰🥰🥰🥰🥰🥰🥰🇧🇩🇧🇩🇧🇩🇧🇩,0,sports
রাজশাহী টিম কে অনেক অনেক শুভেচ্ছা💖,0,sports
সাকিব তুমি আওয়ামলীগ চিন নাই।এখন চিনেনাও আ লীগ কাকে বলে।,0,sports
পাপন সর্কার তার আগে ফাঁসি দিতে হবে সাবধানে যায়নি আবার নাটক চোদায়,0,sports
পাপন এর ফাসি চাই,0,sports
খুলনার ফিল্ডিং বিশ্বমানের এটা মানতেই হবে!!!,0,sports
এগুলো এখন পোষ্ট না করাই ভাল,0,sports
এইটা যে বুদার কইছে আমরা সবাই মিলে চুদে ওরে মহা আকাশে পাঠানো দরকার কি বলেন আপনারা,0,sports
গাঁজা কি জুস্ বানায় খাও???,0,sports
আরে বাই দেব এতো বগ বগ করার কি দরকার বন কর তুই আর কি করবে,0,sports
বিপিএল কে কে ভালো ইনজয় করছেন? 👇👇👇,0,sports
অাজকের খেলাটা অনেক ভালো লাগলো কার কার ভালো লাগলো লাইক দাও তো দেখি,0,sports
সাব্বিরের পিছে লাগছু ক্যা ভাই তোরা?,0,sports
দিনের পাপন সালা আজ তামিম সাকিব মুশফিক ভালনা তাহলে কে ভালো তুর ভাবি হাসিনা ভালো,0,sports
পেছন দিয়ে বাসদিয়ে সামনে এসে মিস্টি কথা। পাপন কাক্কু ধংস অনিবার্জ,0,sports
কুমিল্লার টানা দুইটা ম্যাচ এর জয়ের নায়ক মুজিব।।। দুইটা ম্যাচ ভালোই অনুভোব করলাম,0,sports
লিটন দাস কে কেন বাদ দেওয়া হয় না তার জবাব চাই আগে।,0,sports
ভাইঠিক বলছেন,0,sports
শালা নিজেও জুআ খেলে,0,sports
আমাদের বাংলাদেশের এটাই মানুষের নিয়ম কেউ যদি কোন আন্দোলন করে তার আন্দোলনের ফল কি বাংলাদেশে বাস করি রে ভাই কারে কি বলবো,0,sports
"সাব্বির এর পিছনে লাগছে কেনো বুঝলাম না? প্রথম সেঞ্জুরি উৎযাপন করবেই এটাই স্বাভাবিক,,,আসলে আমাদের মন মানসিকতার প্রভাব পরছে,,",0,sports
অনেক ভালো খেলা হয়েছে‌। আবু হায়দার রনি অনেক ভালো খেলেছে।মালান নিয়মিত ভালো খেলা উপহার দিতে ছে।,0,sports
আমার মনে হয় সাব্বির যা করেছে ভালই করেছে,0,sports
"আপনার রিপোর্ট ভালো লাগে, আপনার কথায় যুক্তি আছে। ধন্যবাদ আপনাকে",0,sports
বানদির ফুয়াইন তে এত বর সাহস কইফায় বুজিনা এরকম একটা নিরহ মানুষ কে হয়রানি করের,0,sports
তামিম ইকবাল খান কে কে ভালোবাসেন লাইক দিয়ে জানি দেন 💓💓💓💓,0,sports
দল থেকে বাদ দে চোর রে,0,sports
এটা কোন রোস্টই হয় নাই!,0,sports
সাকিব ভাইয়া আপনি আবার ফিরে আসেন সব কিছু সমাধান করে বাংলাদেশের মানুষ আপনার পাশে আছে,0,sports
এত কথা কেন হবে 7,0,sports
আজ থেকে আর বছর পর খেলা দেখব,0,sports
মুসি ভাই কি বিশ্বকাপ জিতল নাকি,0,sports
আমি কি গালি দিয়েছি তোমায়,0,sports
পাপন আছে এর সাথে,0,sports
মমিনুল এমন ছয় মারতে পারে বিশ্বাস করেন রাসেল ভাই আমি জানতাম নাহ,0,sports
ভাই অপেক্ষায় ছিলাম আপনার ভিডিওটার জন্যে❤,0,sports
আমি যতদিন আছি সুযোগ নাই,0,sports
পাগলের আলাপ এটা কোন ব্রিপিং হল কিসের সাথে কি বলে জনপ্রিয় খেলোয়ার বা সাকিব তামিম ছারা কারো দিকে তাকানোর সময় আপনার নাই,0,sports
মাইযারে ভিডিওটা না দেখলে তারে সবচেয়ে বড় মিস করবেন আপনার ভিডিওতে,0,sports
যারা কোনো রকমের জ্ঞান ছাড়াই কে গাল দিচ্ছে তাদের জন্যে,0,sports
ক্রিকেটাররা যা করলো খুবই হতাশাজনক এবং খুবই দুঃখজনক সব ঠিক আছে বাট সংবাদ সম্মেলন করে আন্দোলন করা ঠিক হয়নিবাংলাদেশের সকল খেলোয়াড়দের বাংলাদেশের সকল স্তরের জনগণ ভালবাসেতাছাড়া বিসিবি সভাপতিস্বয়ং দেশের সর্বোচ্চ প্রধানমন্ত্রী তাদেরকে ভালবাসেনপ্রতিটি খেলার খবর রাখেনসেহেতু তারা অন্যভাবে সমস্যার সমাধান করতে পারতোপানি ঘোলা করার দরকার ছিলোনাক্রিকেটাদের জন্য সরকার কি না করছেনসরকার সব সময় তাদের পাশে থেকেছেনতারপরও বাংলাদেশ ক্রিকেট টিমকে শুভ কামনা ❤❤❤,0,sports
মনেএকটা কষ্ট থাকতে সোনা চিনলাম না।,0,sports
পাপন কে,0,sports
এভাবেই উৎযাপন করবে তুমি।,0,sports
আচ্ছা সাকিব কেন জুড়ারি সাথে দেখা করতে চেয়েছিল।।। আমার মনে হয় কফি খাইতে🤣🤣🤣,0,sports
বেশি লাফালে এমনই হয়,0,sports
যেই দেশে নবীকে গালি দিলে কিছু হয় না সেই দেশে একজন ক্রিকেটারকে গালি দিলে সব কিছুই ভাইরাল হয়ে হাঙামা শুরু হয়ে যায় কেমন জাতি বুঝি না আজব বাঙালি নিজেই লজ্জিত অনুভব করছি,0,sports
পাপোন্দার এক পা চট্টগ্রাম এক পা ঢাকা বাইন্ধা বিচি দুইটা কুমিল্লা বরাবর ঝুলাইয়া পাশের দেশ বরিশাল থাইক্কা দৌড় দিয়া আইসা কিক মারা উচিৎ 😠কথা কি ক্লিয়ার না ভেজাল আছে 🐸,0,sports
গালি দিএয়াছে ঠিক করেছে ওর মনে অনেক অহংকার,0,sports
পাপন তুই একটা কুত্তার বাচ্চা তুই পদ ত্যাগ করনা হলে তুরে কুত্তা পিটা দিবে জনগণ,0,sports
এই টাই করা দরকার সাকিবকে,0,sports
আহম মোস্তফা কামাল জড়িত কিনা????,0,sports
পাপন কতো পাপি তা বাংলাদেশের মানুষ এতো দিন পরে বুজলো অাজ সাকিবের জায়গায় কেসিনো লোকমান হলে হয়তো এমন হতো না সালা মাগির পোলা পাপন,0,sports
নুনুসুজনপাপনএই তিনজন দায়ী দেশের ক্রিকেট নষ্ট করেছে,0,sports
মাইয়া মানুষের লোভ বেশি,0,sports
হুদাই জেরা কাটতেছে ছেলেটাকে নিয়ে অারে ভাই গালি দেয় নাই মনে হচ্ছে ওরে দেখেই তারপরেও জোর করে ওরে অপদস্ত করতেছে কি যে অবস্হা রে ভাই,0,sports
আরে মাদার চুদেরা তরা কি মানুষ খানকির পোলারা কইছে কি বাল ফালানি দেশে এত কিছু আকাম কুকাম চলে অই গুলার আগে বিচার কর মাগির পোলারা তার পর অই ছেলের বিচার কর,0,sports
মুশফিকের জার্সি পরে ওই হালায় এমন করে কারণ ও মেয়াদ উত্তীর্ণ গাজা খাইছে।,0,sports
সাকিব ইংল্যান্ডের হয়ে খেলুক সেটাই আমি চাই কারণ বিসিবি আর কিছু আবাল আছে তাদের বোজানো দরকার সাকিব কি জিনিস,0,sports
অসম্ভবকে সম্ভব করাই পাঠা রাছেলের কাজ।,0,sports
"রুবেল তর ফেশটা আয়নায় দেখছস?আস্তা কাইল্লা পাডার মত দেখতে,,,হ্যাফির জজ্ঞ ছিলিনা তুই,,দুইদিনে সেলিব্রিটি হয়ে নিজেকে সেলিব্রিটি দাবি করস নাকি,,নিজের ইচ্ছা মতো মেয়েদের মন নিয়ে খেলা করবো,,আর বিয়ে করবো মা বাবার ইচ্ছায় তাইনা,,পাবলিকের উচিত তদের যেমন সেলিব্রিটি বানায়ছে,তেমন ফুতপাতে নামায় দেওয়া,,কিন্ত দেয়না,,ফালতু কোথাকার,,,😡😡😡",0,sports
দুই বছর আগের সংবাদ এখন বাইরে নাকি ফাজলামি পেয়েছেন বাংলাদেশ কেউ প্রতিবাদ করলেই তারের দমানোর পাপনের বিসিবি পদত্যাগ করতে পারেন শাকিবের এখন না খেললে কিচ্ছু হইব না কিন্তু বাংলাদেশের ক্রিকেটের ধ্বংস হইবো তাই ভাবিয়া করিও কাজ করিয়া ভাবিও না সবচেয়ে বেটার নাজমুল হাসান পাপনের ক্রিকেট থেকে অবসর নেওয়া পাপন তুমি বললো না এটা স্বাধীন দেশ,0,sports
🤣🤣🤣🤣এই বয়সে না করলে কি বুড়ো বয়সে করবে🤣🤣🤣🤣🤣🤣,0,sports
খেলাইছো কয়বার সত্যি কথাটা বল রুবেল,0,sports
দেখেন ভাই সে অনুতপ্ত তাকে মাফ করাই যায়। আমাদের প্রিয় নবী কে যখন গালি দিলো তখন কেউ এগিয়ে আসেন নাই। যাক গিয়ে তারে অনেক অপমান করছেন মাফ করে দেন।,0,sports
পাপন বড় মদ খোর গাঁজা খোর,0,sports
কুমিল্লার জয়ের একমাত্র নায়ক মুজিবুর রহমান। অসংখ্য ধন্যবাদ আফগান ভাই তোমাকে। 👇🇧🇩💗,0,sports
অবশ্যই ব্যাক্তি স্বাধীনতা সবারই আছে তবে অন্যের ব্যিক্তিগত কথা অনুমতি ছাড়া প্রোচার দন্ডনিয় অপরাধ শুধু মাত্র ব্যাবসা ওTRPর জন্য মানুষকে হেয়োপ্রোতিপন্য করাটা অপরাধ টেলিভিশন চ্যানেলের অফিসগুলোতে কি হচ্ছে সে খবরতো কোন সাংবাদিককে দিতে দেখিনা কিংবা কোন টেলিভিশন মালিকএর অপকর্ম নিয়ে রিপোর্টকরতেতো দেখিনা সাংবাদি নামের সাংঘাতিক যতসব ফালতু৷ সফল ছেলেদের পিছনে টাকার জন্য মেয়েরা নিজ ইচ্ছেতেই ঘোরে এখানে সবদোষ মেয়েমানুষের তারকাছে মেয়েরা যাচ্ছেকেন?,0,sports
ঢাকা এত বাজে খেলবে এটা ইম্পসিবল কি বাল খেলছে মাদারচোদেরা,0,sports
নাজমুল হাসান শান্তর ভক্তরা কোথায় লাইক হবে👍👍,0,sports
এখানে যারা আসবেন সবাই বকা দিবেন তোমরা জুনিয়রদের সাথে রানে অলআউট হবা আর আমরা কিছু বলতে গেলে মাইন্ডে লাগে।,0,sports
সাকিব ছাড়া বাংরাদেশ অসম্পুর্ণ।,0,sports
শালাগ আর কন কাম নাই ওনার মন চাইচে গালি দিতে গালি দিচে তাতে সমসসা কথাই ওনি সামনা সামনি গালি দিচে ভলেকি ওনার দস হএচে বাহিরে তো বোহু মানুস গালি দেই তাদেরকে দরেনাকা 😠😠😠,0,sports
অবিলম্বে পাপনের পদত্যাগের দাবি জানাচ্ছি,0,sports
আজম নাসিরের সন্ত্রীস বাহিনী গেল ত গ্যালারী ভতি হয়ে যাই,0,sports
এবার বিপিএলে রাজশাহী সেরা। রাজশাহীর সামর্থকেরা কই সারা দিন। 👇👇,0,sports
রাজশাহী কাপ নিবে,0,sports
বদমাইশ,0,sports
খুলনার ভক্তরা কই লাইক দাও প্লিজ,0,sports
সাকিবুল হাসানের সাথে অবিচার করা হয়েছে,0,sports
বদমাশ চেনেল,0,sports
ভাই আমার একটা প্রশ্নকতটা পাপ করলে পাপন হওয়া যায়??,0,sports
বোডের প্রদান মুখ্য পাএ এই প্রথম,0,sports
সাব্বির কে দল থেকে বাদ দেয়া হোক,0,sports
মুসফিক এর ভক্তদের দেখতে চাই লাইক দাও,0,sports
পাপন নান্নু সুজন কে বের করে দেয়া হোক,0,sports
সত্যি কথা বলেন নাকি,0,sports
রুবেলে।কথা।গুলো।ভালো।লাগলো,0,sports
বর্তমান বিসিবি প্রধান পাপন বনাম সাবেক বিসিবি প্রধান অর্থমন্ত্রী কামাল।তুমরা বুঝ আমার বাল।খেলা চলছে।সামান্য বিপিএল এর দল না পেয়ে কামাল সাহেব ক্রিকেট নিয়ে রাজনীতি করছে।এ ছাড়া আর কিছুই নয়।,0,sports
সাকিব নাই বাংলাদেশেৱ খেলা বন্দ হয়ে য়াবে,0,sports
অন্য দেশের খেলোয়াড়দের মতো বাংলাদেশের খেলোয়াড়দের সাদিনতা নাই!এতে বাংলাদেশ খেলোয়ারের মানহানি হয়!বাংলাদেশ টিকেট বোডের পরিচলায়া এতোটা বালো নয়খেলোয়াড়দেরকে জিম্মি করে রাখে!,0,sports
যে সময় ওভারে এর বেশী থাকবে তখনই মুস্তাফিজুর কে বল করতে দেওয়া উচিত,0,sports
পাপন সাহেব এরকম একটা সুযোগের অপেক্ষায় ছিলেন বোকা সাকিব তাবুতে পারল না,0,sports
হুদাই,0,sports
এটা কোন দরনে গেম,0,sports
এগুলি এখন পাপনের আর সুজনের আর নাইমুর রহমান দুরজয় নান্নু আরো আছে তাদের কার সাজি আমরা বাংলাদেশের মানুষ এতো আবার আবালনা বিসিবি বুজেসাউ,0,sports
না সিন্ডিকেট বস পাপন।,0,sports
আমি খুলনার ছেলে সিলেটের বন্ধুরা তোমাদের দল কিন্তু এবার অনেক দুর্বল এটা তোমাদের মানতে হবে।,0,sports
পাপনের সেচ্চায় পদত্যাগ করা উচিৎ,0,sports
বাংলাদেশের সব দর্শক সবাই যে যেখানে দেশের যে যে প্রান্তে আছেন ক্রিকেট বর্জন করুন। টিকেট কিনা থেকে শুরু করে স্টেডিয়াম যাওয়া। সবকিছু সবকিছু।আইসিসি বিসিবি সবাই দেখুক এক সাকিবের জন্য পুরো বাংলাদেশ এক।এভাবেই হোক প্রতিবাদ দূর্বার আন্দোলন।,0,sports
তুমার সময় কি বাল ফালাইছে,0,sports
আপনি যেই হোন না কেন একজন বাংলাদেশের খেলোয়াড় কে কেন গালি দিলেন আপনি কার কারনে মুশফিককে গালি দিলেন দর্শকের সামনে বলতে হবে যাদের জন্য আমরা একটু বিনোদন পাই তাদের উপর কেন আপনার খারাপ আচরণ,0,sports
কম পানির মাছ বেশি পানিতে পরলে জাহ হয় আর কি <br /><br />আগে ভাত পাইত নাহ এখন যে ভাব চুদাও,0,sports
পাপইননা,0,sports
আজকের এই আন্দোলনটি জদি সব ক্রিকেটার এবং দেশের সব জনগন মিলে ইসলামের পক্ষে করতো।খুব ভালো লাগতো।,0,sports
পাপনের বিচার একদিন হবে বাংলার জমিনে,0,sports
আমি সভ বুঝি খেলা টা কম বুঝি কিন্তু খেলার সভ খবর দেখি তাই বুঝি পাপন এর মেয়ের সাথে সাকিপ নাকি এক রাইত কাঠাই ছে তাই পাপন যেনে কোনো না কোনো একটা বের করে তাকে বাদ দেওয়া হয়তে ছে তা না হলে এসভ বিষয় নিয়ে কেনো বাদ দেওয়া হয়তে ছে সরি ভুলে একটি কথা বলে ফেলার জন্য আর এক কথা না বলে পারি না আমি মর লে মাঠির তলে যাবো মিথ্যা বলে সাছতি দেবেন আল্লাহ আমি টি বাংলা দেশের খেলা দেখবো না সামনের যত খেলা আসোক যত দিন সাকিব নাই তত দিন ফেইসবুক কোনো খেলা চলবেনা সাকিব এর বক্ত রা কি বলো হাত টা উপরে দেও দেখি এভাবে🖖🖖🖖🖖🖖🖖🖖🖖🖖🖖🖖🖖🖖🖖🙌,0,sports
পাপন কবিতাহেইইই নাম আমার পাপনক্যাসিনো ছাড়া ত্রিভুবনে নেইকো কিছু আপন।চিন্তায় আমায় নইকো কিছু ক্যাসিনো আর জুয়া ছাড়াআমিই এখন ক্রিকেটকে দিচ্ছি হোগা মারাযতই তোমরা গালি দেও যাবো না বোর্ড ছেড়েআমার মতোই যাবো আমি ক্রিকেটের হোগা মেরে।,0,sports
আজ যদি ম্যাচটা মিরপুরে হত তাইলে কি হতো? বলতো wicket issue.,0,sports
কয়েকদিন পর সাকিবের পা ধরার জন্যে রেডি থাকো বাছা।🐸,0,sports
প্লেয়ারদের কোনো লজ্জা নাই হারার পরেও বলে কোনো ব্যাপার না এখন বাংলাদেশ এমন একটা স্থানে পৌঁছাইসে যখন অস্ট্রেলিয়ার সাথে হারলেও সেটা খারাপ রেজাল্ট; সেখানে আফগানদের সাথে হেরেও সাকিবের কোনো ভাবান্তর নেই,0,sports
এক বালতি ভর্তি দুধ হারাম করার জন্য এক ফোঁটা চনামলমূত্র যথেষ্ট। তেমনি বাংলাদেশ ক্রিকেট ধ্বংস করার জন্য বর্তমান বিসিবি কমিটি বৃন্দ ই যথেষ্ট। যতদিন বিসিবির সভাপতি থেকে শুরু করে কমিটির পি এ পর্যন্ত বরখাস্ত না হবে ততদিন পর্যন্ত আমাদের দেশের ক্রিকেটাররা ফিক্সিং মুক্ত খেলা খেলতে পারবেনা এটা আমার বিশ্বাস। বিশ্বাস না হলে জরিপ করে দেখুন কমিটি বৃন্দ হওয়ার আগে তাদের অর্থ সম্পদ কত ছিল আর এই মুহুর্তে কত আছে। আমার কাছে মনে হয় ক্রিকেটারদের থেকে বেশি ইনকাম তাদের হয়।আর হিংসাত্মক মনোভাব নিয়ে কখনো অভিভাবকের দায়িত্বে থাকা যায়না! এদের ছোবল থেকে,0,sports
ধন্যবাদ মোবাশ্বের আংকেল!পাপনের গোমর ফাঁস করে দিয়েছেন।,0,sports
প্রিয় বন্ধুরা বিয়ে করে দাম্পত্য জীবনে সুখী থাকতে হলে একটি উপদেশ মেনে চলুন উপদেশ টি ভালো লাগলে চ্যানেলটি সাবস্ক্রাইব করবেন,0,sports
আমি ইউটিউবে করি।।কিন্তু কারো সাপোর্ট পাচ্ছি নাআমার চ্যানেলটা করুন,0,sports
পাপনকে রিমান্ডে নেওয়া হোক,0,sports
জুয়াড়ি পাপন মুক্ত বাংলাদেশ ক্রিকেট ম্যানেজমেন্ট চাই।,0,sports
মুশফিক ভাই তো বড় আর ছোটরা তো ভুল করতেই পারে তাছাড়া ওই ছেলে তো ছরি বলছে তাও কেনো এভাবে ওকে আটকে রাখা হয়ছে। আমারা যাই যা বলি না কেনো। আমি ও তো ক্রিকেট খেলি। আমারা বড়ভাইদের কে অনেক কিছু বলি কই তারা তো মন খারাপ করে না,0,sports
যখনই অলক কাপালী ব্যাটিং এ নামে তখনই শামীম আশরাফ রাম ছাগল বলে সিনিয়র সিটিজেন । তো ফরহাদ রেজা কি ইয়াং বয় ? আফ্রিদি রাসেল ফ্রাইলিংক সোয়েব মালিক এরা কি শামীম আশরাফের মেয়ের জামাই লাগে ? গলা দিয়ে কথা বের হয়না তাও শামীম আশরাফ এত বছর ধরে ধারাভাষ্যকার এর চেয়ে বড় কৌতুক আর কি হতে পারে যে বাংলাদেশের মত ক্রিকেট পাগল দেশে শামীম আশরাফের মত বকরী ছাগল ধারাভাষ্যকার !! না আছে কণ্ঠ না আছে চেহারা না পারে ফ্লুয়েন্ট ইংলিশ বলতে ।,0,sports
পাপন হটাও ক্রিকেট বাচাও।,0,sports
সবাই তো আপন না ওনেকেই হয় পাপন😈😈,0,sports
ইসলাম প্রিয় ভাই ও বোন সবাইকে আমার ইসলামিক চ্যানেলে আমন্ত্রণ সমায় পেলে একবার ঘুরে আসবেন,0,sports
সবই বুঝলাম কিন্তু অাপনারা আবালের মত তার নাম্বারটা দেখাইছেন কেন?,0,sports
এই পরিমাণ লুচ্চা! ছিঃ! এরা অরুচিতে পরিণত হয়েছে।,0,sports
মাদারের বাচ্চা গাজা খায়ছ,0,sports
তার মানে তার জীবনের কনো ভালো লাগে ভালোবাসা বলে কিছু নেই,0,sports
মুস্তাফিজ যে বাংলাই বললো সেটাই ভালো লাগলো,0,sports
মুশফিক ভাইয়ের কাছে আশা করছি ছেলেটাকে মাফ করে ওকে কিছু যেনো না করে।।,0,sports
রুবেল এর মুখে বা ঠোটে মেরিল দেওয়া উচিত,0,sports
সব দালের বাচ্চা,0,sports
সাকিব ♥♥♥♥♥,0,sports
আসসালামু আ্লাইকুম।হ্যপি আপু আপনার কথা শুনে আমি যতটা ভেবেছি আপনি সত্য কথা বলছেন। আর একটা কথা হল আপনি একটা মহিলা হয়ে ওতো রাতে রুবেলের বাসায় কেনো যেতেন?কারন গাওয়া ঘি আগূন পাশা পাশি থাকলে তো গলবেই এতে কোন সনদেহ নেই।মেয়েরা নিজের ইজজত নিজে বিলিয়ে বেড়ায়।হ্যপি আপু শোন আপনি আর রুবেল জানয়ার ।যে কু কাজ অবৈধ্য মিলন করেছো এটা মহাপাপ আপনারা জেনা ব্যভিচার করেছেন।যদি হাদিস কোরান অনুযায়ী বিচার করা হয়।তাহলে বুক সমান গত্য করে। সততরটা পাথর আপনার শরীরে নিক্ষেপ করতে হবে।এটা আমার কথা নয়?যদি হজরত ওমর ফারুকে আজম। নবী পাকের একজন জলীলুর কদর সাহাবা ছিলেন। উনি যদি থাকতেন তাহলে মিত্যু দনডের আদেশ দিতেন। যাইহোক আপনারা শয়তানের কবলে পড়ে একটা কবিরা গোনাহ। কঠিন শকতো পাপ করে ফেলেছেন আর কোনো হাত নেই।।একবার যে থুথু মাটিতে নিক্ষেপ করলে সেটা আর ফেরত নেওয়া যায় না ।তবে একটা উপায় আছে হ্যপি।আমার আললাহ খুব দয়ালু আললার কাছে অঝর নয়নে ঝর ঝর করে কাদুন আমার মনে হয় আললাহ ক্ষমা করবে।ইনশাআললাহূল আজীজ আর কখনো যেনো এ ধরনের পাপ করবেন না।,0,sports
এসব বস্তি পোলাপান জাতীয় টিমে জায়গা পাই কিভাবে? 😠😠😠😠,0,sports
সোহাগ গাজী ভাইয়ের জন্য সুপার ওভার দেখতে পেলাম।,0,sports
দয়া করে আমার চ্যানেলটি সাবস্ক্রাইব করুন,0,sports
গাল দিছে বাল হইছে,0,sports
বিশ্বকাপের ম্যাচ গুলো দেখলে মনে হয় সালারা পজিশন আর পারিশ্রমিকের জন্য খেলেছে। দেশ প্রেম নেই,0,sports
রাসেল কে ক্যাপটেন না দিয়ে দেশি খেলোয়ারদের ক্যাপটেন দিলে খুশি হতাম,0,sports
আপু আপনি সুবার থেকে অনেক অনেক ভাল,0,sports
আর মাত্র কয়েকদিন বাকি দেখে নিন কুরিয়ার ফ্রি ভিসা এর আবেদন প্রক্রিয়া,0,sports
আমার পছন্দের খেলোয়াড় ইমরুল,0,sports
পাপন সাহেবের কাছে কোন সমস্যাই না মনে হয়। আপনি এবং আপনার শিসরা পদত্যক করেন এইটাই চায় কোটি মানুষের।,0,sports
ভাইয়া আমরা সবাই সাথে আছি আপনি ও ক্রিকেট টিম এগিয়ে জাগ,0,sports
কুমিল্লার ঠা বাজে পেংল্লি ং কারণে এতো রান হয়েছে,0,sports
সাব্বিরকে 1 বছরের জন্য মাঠের বাইরে রাখা হোক,0,sports
"ফালতু ছেলে, ওকে টিম থেকে বের করে দেয়া হোক",0,sports
অই জারছি পরা লোক টা কে পাইলে কোত্তার মতো পিটাইতাম,0,sports
বোকা বছর গোপন ছিলো কিভাবে? বসের শাস্তি হইছে বছরের ঘটনা নিয়ে।।,0,sports
আমি চাই বাংলাদেশি কোচ চাই বিদেশি কোচ দরকার নাই,0,sports
ফকিন্নির বাচ্ছাকে ক্রিকেট থেকে বাদ দেওয়া দরকার,0,sports
খুলনা জিতবে দেখবে দেশ,0,sports
গালি দিছে ভালো করছে প্লেয়ারের চোখ কান থাকবে খেলার মাঠে গ্যালারিতে না,0,sports
সাব্বির একজন জাতীয় দলের খেলোয়াড় তবে দেশের জন্য সে মাঠে কিছুই করতে পারেনি আজ পর্যন্ত। তাকে নিয়ে কেন এত মাথা ব্যাথা আর কেনই বা জাতীয় দলে বার বার সুযোগ দেওয়া হয় বুঝিনা আমি।,0,sports
এসব মেয়েদের কাজই ব্লেকমিল করা,0,sports
পাপন কে বিসিবি থেকে বাদ দেয়া হুক কারন সে নিজের বুজটা বিসি বুজে,0,sports
কোটি মানুষের ট্যাক্সের টাকায় আচুদা খেলা খেলবো গাইল্লাইবোনা বাল ফালাইবো পারছে পুলাডা একা ছিলো।,0,sports
পাপনের বলির পাঁঠা সাকিব।তার মানে অন্য কোন খেলোয়াড় যেন বিসিবির সভাপতির বিরুদ্ধে কেউ দাঁড়াতে না পারে,0,sports
আপনারে কি জানেন ভারতের পা চেটে কি পেয়েছে দেশ,0,sports
একমাএ ভাঙ্গালিরা নিজের ভাষার বিতর অন্য ভাষা ডুকায়ভাই পাপন এত ইংলিশ ফুটাস ক্যানবাংলায় বলতেছ সব বাংলায় বল।ইংলিশ বল্লে সব ইংলিশ বল।,0,sports
বস আমলা😍😍😍 খারাপ করলো😭,0,sports
ধুর মিয়া মেসি রোনালদো নিয়া কবে রিপোর্ট করবেন? মেসি রোনালদো বিয়ার আগে এত বাচ্চা নিল যে? মানুষের ব্যক্তিগত লাইফ নিয়া ছ্যাঁচড়ামি করেন দুদিন পর পর।,0,sports
আপনি মিথ্যা বাদি,0,sports
মাথা,0,sports
রুবেলরে মেয়েরা স্বামী বানানোর স্বপ্ন দেখে ????? কোন মেয়ে ভাই ???,0,sports
ভুল বোঝাবোঝা ভুলে সব ঠিক হবে আশা করি,0,sports
দেব এর কথা গুলো মনে হচ্ছেসে এর প্রতিনিধি তিন মোরলের গন্ডি তারা ভাল ভাল প্লেয়ার দের ফাঁদ তৈরি করে এবং সে ফাঁদে ফালানো হয়,0,sports
হাহাহা,0,sports
সব চাইতে লিটনের খেলা ভালো লাগছ,0,sports
পাপের পদত্যাগ চাই।।,0,sports
"ভাইয়া মেয়েরা যদি ওর কাছে আসে তাহলে ওর দোষ কোথায় , ওর দোষ এটাই যে ও একজন জাতীয় দলের খেলোয়াড়,,,,pic এ দেখা যাচ্ছে মেয়েদের মত আছে,, তাহলে মেয়ে গুলারে পিটানোর দরকার সাব্বির ভাইকে নয় ,, তবেই খারাপ মেয়েরা ঠিক হবে,,,",0,sports
আজাইরা 😂😂😂,0,sports
মুস্তাফিজ কে যদি একটু বেটিং শিখায় তাহলে মুস্তাফিজ আরও ভালো বেটিং করতে পারবে ইনশাল্লাহ যদি মুস্তাফিজের আত্ববিস্বশাসি থাকে,0,sports
পাপন নিজের দোষ ডাকতে এখন সাকিবের পিছনে লেগে গেছে 🖕🖕🖕,0,sports
সাব্বির কোন ভুল করেনাই।,0,sports
বল টেম্পারিং করল স্মিথ আর ওয়ার্নার সাজা হলো মাস। ম্যাচ ফিক্সিং করল না শাকিব সাজা হলো এক বছর। হায়রে আইন হায়রে বাংলাদেশের ক্রিকেটকে নষ্ট করার ষড়যন্ত্র।।,0,sports
সিলেট হারলো তাদের বাজে ফিল্ডিং এবং বাজে অধিনায়কত্বের কারণে সবচাইতে বড় ব্যাপার হলেও তাদের অধিনায়ক বলতে কেউ নেই।,0,sports
সঠিক টা জেনে তার পর নিউজ করুন,0,sports
তেমন ভাল হয় নাই বার বার লাইফ পেয়েও ইনিংস লম্বা করতে পারে না ন্যাশনাল টিমে তো আরো খারাপ খেলবে,0,sports
ঢাকা প্লাটনের জয়ে কে কে খুশি লাইক দিন,0,sports
ওর ছবি দেখে মনে হয় ও লুচচা,0,sports
পাপানের পদতে করা হোক,0,sports
মনে হয় না আর বাংলাদেশের খেলা দেখা হবে,0,sports
পাপন কাকু নাটক কইরো না। 🤫,0,sports
এই উদযাপনে তো বেয়াদবির কিছুই নেই।,0,sports
যারা অনলাইনে বেটিং করতে চান বা ক্রিকেট ফুটবল সহ অন্যান্য সকল খেলায় বেট বা বাজি ধরতে চান কিন্তু বেট একাউন্ট না থাকায় বেট বা বাজি ধরতে পারছেন না বা পর্যাপ্ত ডকুমেন্ট না থাকায় বেট নেটেলার অথবা স্ক্রিল একাউন্টস বানাতে পারছেন না এই পোস্ট টি শুধু মাত্র তাদের জন্য। ফুল ভেরিফাইড এবং সকল প্রকার ডকুমেন্টস সহ নিচের দেওয়া একাউন্টস গুলো আমার কাছে পাবেন সবসময়। স্টক এভাইলেবল। 👉 ( )👉 👉 ( )👉 ( )👉 যে বা যারা বেট নেটেলার অথবা স্ক্রিল একাউন্ট কিনতে আগ্রহী তারা আমার সাথে যোগাযোগ করুন,0,sports
গাজা খোর,0,sports
পালতু কথা <br />সব মিত্তা কথা,0,sports
"কথায় কথায় ঠিক আছে,,,,,,,,হ্যা হ্যা হ্যা",0,sports
আজকে খেলবো পাপনকে নিয়ে,0,sports
কোটি টাকা বোনাস দিছেন চার লক্ষ টাকা বেতন দিছেন তাহলে জাতীয় দলের মোশারফ এর চিকিৎসার জন্য মানুষের দুয়ারে দুয়ারে ঘুরতে হয় কেন পুরাতন অনেক খেলোয়ারদের মানবতায় জীবন কেন কাটাতে হচ্ছে আপনার কথায় যদি ধরে নেয়া যায় তাহলে খেলোয়ারদের তো কোটি কোটি টাকার মালিক হয়ে যাওয়া কথা দেশবাসীর কাছে অনুরোধ এই বিপদ কালে সাকিব মুশফিক তামিমদের পাশে দাঁড়াই পাবন মিথ্যাবাদীর কথা আপনারা কেউ খেলোয়াড়দেরকে ভুল বুঝবেন না এখানে পাপন জ্বালা উদ্দিন নাঈম রহমান দুর্জয় সুজন আকরাম খান এদের সবাইকে পদত্যাগ করে নতুনভাবে বিবিসি সাজানো হোক দাবি মোদের একটাই পদত্যাগ চাই,0,sports
জানোয়ারের বাচ্চা সাবির রহমান।,0,sports
ধন্যবাদ ভাইয়া ভন্ডদের বিরোদ্ধে কথা বলার জন্য💚,0,sports
সাকিব ভাইয়ের নাম্বার উইকেটের আবেদন 😂🤣😃😄😍,0,sports
অন্যায় দাবি করছে ক্রিকেটাররা অথচ দোষ নাকি বোর্ডের ? বাংলাদেশ মাতালের কারখানায় পরিনত হয়েছে।,0,sports
ফাক সালা রা সেম তাকসিন,0,sports
গালি দিছে তে কি হয়েছে এমন যে বাল খেলছে বললেও দোষ। বেতন বাড়াইছে ভাল না খেলি দেখুক এবার হালারা,0,sports
ঠকে গেল মনে কোন দুঃখ নাই হাহাহা,0,sports
শুধু ক্রিকেট না ভাইয়া পুরো বাংলাদেশ ধ্বংস করে ফেলছে।,0,sports
পাপন কে গার দাকা দিয়া বিবিসি তেকে বের করে দেওয়া হক,0,sports
নাছির ভাই কে আমরা আবার দেখতে ছাই,0,sports
এটা পাপনের সরো যন্তো,0,sports
ভারত কখনো বাংলাদেশের ভালো চাই না,0,sports
আসেন আমরা সবাই মিলে জনাব পাপনের পদত্যাগ চাই। আমাদের ক্রিকেট কে বাঁচাতে হবে।পাপনের পদত্যাগ। পাপনের পদত্যাগ।পাপনের পদত্যাগ।পাপনের পদত্যাগ।,0,sports
মুসফিক রহমান,0,sports
সাকিবের জন্য আমি নিজে কেঁদেছি।,0,sports
ইউটিউবে টাকার জন্য কেন মিথ্যা কথা লিখে মা বাবাকে কেন গালি শুনান ।।,0,sports
রুবেলের জন্য শুভকামনা রইলো,0,sports
আচ্ছা এনামুলের হাই স্কোর কত,0,sports
এজন্য ক্রিকেট চোদিনা ফোটবল বেশ্ট,0,sports
ভাই ঠিক বলছেন আর বলতে ইচ্ছে করছে,0,sports
পাপন কে দিনের দায়িত্বে দিল কিকেট বোডের জন্য ।প্রধান মন্ত্রী আজ পাপন সারা জীবনের জন্য কিকেট দায়িত্বে বসে গেল ও খানে কোন নির্বাচন হয় না। বোডে পাপন যাকে কে ইচ্ছে তাকে নির্বাচিত করে। তাকে বিচারে আওয়াতা আনা হোক।,0,sports
এই খানকির পোলারে মাশরাফির অনুরোধে দলে নিছে আমার বাল ফালাইছে।।,0,sports
সৌম্য সরকার কে বাদ দেওয়া হোক,0,sports
পাপনকে দেখলে আমার ঘৃণা হয়,0,sports
ভুয়া খবর তো ভালোই তো প্রচার করতে পারেন । সালার মিডিয়া এজন্য বাংলাদেশের চ্যানেলের খবর দেখতে পছন্দ করি না । ওখানের সত্য ঘটনা না জেনে ভুয়া খবর কিভাবে প্রচার করেন আমার মাথায় ঢুকে না । ওখানে কোনো বাক বির্তক হয় নি ।,0,sports
আমাদের সিলেট আজ নতুন ইতিহাস করে দেখালো,0,sports
ভাই পাপন সাব ছাইলে এটা সমাধান করা জায় নাটকের কি দরকার,0,sports
আজীবন নিষিদ্ধ করতে হবে।,0,sports
সালা রা মাহমুদ উল্লারে কিসের জন্য দলে রাখা হয় ডিম খাইতে।।। নির্বাচক পাল্টান টিম ভাল করবে,0,sports
পাপন কে সবাই জুতা মারেন,0,sports
একজনকে জুয়াড়ি বহুৎ বড় মাদারচোদ পাবনীক্রিকেট বোর্ডের চেহারমান হয়ে থাকার কোন যোগ্যতাই রাখেনাযেখানে একজন জুয়াড়ির ভিডিও সরাসরি ভাইরাল সেখানে কি করে এখনো টিকে থাকে আমি বুঝি না আমার সোনার বাংলায় সোনার বাংলা।,0,sports
আমার কেনো জানি মনে হয় সাকিব আর বাংলাদেশের হয়ে খেলবে না।,0,sports
পাপন হাটাও টিকেট বাঁচাও পাপন এর সব ষড়যন্ত্র,0,sports
নাম্বার দফা দাবিপাপনের পদত্যাগ,0,sports
ফকিরনি আর কি হবে,0,sports
চোদনা সাব্বির,0,sports
এটা মাঠ না মানচিত্র😂,0,sports
বিয়া করালে তো হয়,0,sports
পাপনের জোয়া খেলার ভিডিও ভাইরাল হইছে।কিন্তু কোন টিভি চ্যানেলে তা এখনো ভাইরাল না হওয়ার কারন হলো। বাংলাদেশে যত টিভি চ্যানেল আছে সব ঘোষ খোর সালা সব ঘোস খোরের বাচ্চা ঘোস খোর।,0,sports
পাপন্দা ভরপুর টাকা খেয়েছেআইসিসি দিয়েছে।সাকিবকে এই সিরিজ থেকে বাদ দেওয়ার জন্য টাকা খাইছে।,0,sports
রিয়াদ,0,sports
আজীবন নিষিদ্ধ করা উচিৎ।।,0,sports
সাকিব দেশ প্রেমিক নয় শাকিব একজন অর্থ প্রেমিক অলরাউন্ডার,0,sports
ওরা চাকর নয়,0,sports
এই ছেলে কে যে দরে রেখেছে সেত বাবা গুর দেখেই যা,0,sports
ডেভিড মালান আইপিএল খেললে ভালো হতো অসাধারণ খেলোয়াড়,0,sports
ছোটলোক জাত,0,sports
অসাধারণ,0,sports
কিছুক্ষণ আগে সাকিবের বিপক্ষে ছিলাম। এখন আপনার ভিডিও টা দেখে শেষ পযন্ত তার পক্ষেই চলে আসলাম ❤❤ সাকিব ভাই❤❤,0,sports
ব্যানারে উইকেট কেন?,0,sports
বাঙগালিদের ব্রেন ওয়াস করা খুবি সহজ আমি পাপন ভাই এর পক্ষেআজকে হাতুরু সিংহ আমাদের ক্রিকেটেরউন্নতি করেছে তাকে আমারা অপমান করেছি। এখন আমরা পাপন ভাই এর সাথেও একি কাজ করছিহায় রে মুর্খ বাঙগালি যারা করতে চায় উপকার তাদেরই করি অপকার,0,sports
আমি খুশী,0,sports
তাসকিন ভাই সেরোকম বিডিও মাইরটা যোস,0,sports
সাকিবকে সম্নান দেয়ার মত এই দেশে মানুষ নাই আমার মতে সাকিব ওন্নয় দেশের হয়ে খেললে বাল হবে,0,sports
গতদিন আগে পাপনের প্রকাশ পায়। কিন্তু এটা নিয়ে কেউ কোনো কথা বলছে না। আপনার মনোযোগ আকর্ষণের চেষ্টা করছি,0,sports
আমার বিচারে লয় ওরে একেবারে বাদ দেওয়া হোক,0,sports
তাহলে আপনি এখন কি করতে চান ষড়যন্ত্রকারী হিসেবে সাকিবকে অথবা তামিমকে জেলে ভরে দিতে চান?,0,sports
অনেক ভালো,0,sports
পাপন কাকা ঠিক কথা বলেছেন✌✌✌✌,0,sports
পাপন ভাই সাকিব ছাড়া বাংলাদেশ ক্রিকেট অচল তাই সাকিব ভাইকে মুকওি হক দুই বছরের শাস্তি থেকে আপনারা সবাই কি এক মত তাহলে লাইক করেন,0,sports
এই জন্য বাংলাদেশের এই অবস্থা আমরা ভালো জিনিসের কদর জানীনা😥😥😭😭সাকিবের কিছু হবেনা। যা হবার বাংলাদেশের হবে ! কাস এটা বুঝার মতো মাথা থাকতো????,0,sports
তাসিকিন ভাই অনেক সুন্দর হা হা হা আপনে পারেন বটে ভাইয়া ভালো আচেন,0,sports
যে জীবনে ক্রিকেট খেলেনি সে হয়েছে সভাপতি ক্রিকেটের মধ্যে পাপন রাজনীতি ঢুকাচ্ছে,0,sports
জার্সি পরা কুকুরটা কে মার এক জন সাধারন মানুষ কে হয়রানি করার ক্ষমতা পায় কেমন করে,0,sports
"ধন্যবাদ তাহমিদ ভাইয়া, সাব্বিরের বেলায় সব দুষ, নিন্দুকরা নিন্দা করার বিষয় পায়না তাই এমনে করতেছে, নিন্দুকদের ভালো উদাহরণ দিছেন।",0,sports
বাহ্ দারুন তো! সাকিব ম্যাচ ফিক্সিংয়ের অফার ফিরিয়ে দিয়ে দেশ প্রেমের এতবড় পরিচয় দিলো কিন্তু বিসিবি কে না জানানোয় এখন তাকে বহিষ্কার করা হচ্ছে!!! শালার ফকিন্নির বাচ্চা সব তগোরে জানাইলেই কি? আর না জানাইলেই কি? কোন বালটা ফালাইতি? সাকিব তগোরে কয়নাই ভয়ের চোটে কারণ তোরা শুনলে বলবি ;সাকিব অফারটা ল ম্যাচ ফিক্সিংয়ের টাকা আমরা ভাগ কইরা নিমুনে। আর ধরা খাইলে দোষটা জামাত বিএনপির উপর চাপায় দিমু;।,0,sports
আমার মনে হচ্ছে লোকটি গালি দেয় নি মুশফিক ভাই ভুল শুনছে,0,sports
পাপন ভালো মানুষ,0,sports
"বিষয় টা কি,,,, না জেনে কি শাওয়ার অভিযোগ।।।।",0,sports
ঠিক এই মুহূর্তে আপনি ভিডিওটি প্লে করে কমেন্ট পড়ছেন। কথা ক্লিয়ার নাকি ভেজাল আছে😊😊😊আচ্ছা ঐদিন কাসিনোতে পাপন জিতছে নাকি হারছেকেউ কি জানেন🤔🤔🤔,0,sports
এবারের বিপিএল মাঠ হচ্ছে কুতকুত খেলার মাঠের সমান তার উপর পুরা ব্যাটিং ফিস এরপরও বাংলাদেশী ব্যাটসম্যানরা দড়ির আশেপাশে ছক্কা মারে।,0,sports
আমাদের দেশের খেলোয়াড়দের তেল হয়ে গেছে বেসি,0,sports
তুমি পাপন একটা অনেক বরো চালবাজ,0,sports
দুনিয়ার অনেক মানুষ দেখেছি কিন্তু রুবেলের মত খারাপ মানুষ দেখি নাই,0,sports
তাদের টা দাবি ছিলযার মধ্যে টা ছিল বেতন বাড়ানোবিসিবি শুধু টা দাবির উত্তর দিছেবাকি গুলোর উত্তর দেই নি।।এর দ্বারা বুঝা যায়বিসিবি ব্যর্থ।তাদের পদত্যাগ করা উচিত,0,sports
ভোলার মাদ্রাসার ছাত্র গুলো নিহত হওয়ার ঘটনা কে ভূলিয়ে দেওয়ার বাহানা 🤔🤔🤭,0,sports
আমার মনে হয় পাপন ও তার পরিবারের লোকেরা খেলতে চায়,0,sports
ভাই আপনার রিপোর্ট গুলো আমাদের খুব ভালো লাগে,0,sports
বিনোদন😁😁🔫🔫,0,sports
এটা ভারোতের চাল,0,sports
এই সামার ফোর মাইয়ারে বিরাটদের সাথে খেলার জন্য ভারত সফরে পাঠানো হোক,0,sports
বেস্ট ম্যাচ,0,sports
খুবই ভালো করেছে সাকিব,0,sports
এইগুলা বাংলাদেশের মানুষ সবাই এখন জানে কে করেছে। আজ আমার সালের রাজাকারদের চেহারা খুব দেখতে ইচ্ছে করছে।তাদের চেহারার সাথে আজকে আমাদের ক্রিকেটকে ধ্বংসকারী রাজাকারের চেহারাটা মিলিয়ে দেখতাম।,0,sports
পাপনের চাল সব কিছু,0,sports
এই সালা নিজেও ভারতের দালাল। পাপন নান্নু সুজন এরাতো আছেই।,0,sports
আপনার সাথে সহমত তবে সাকিব একটা বেয়াদব ও বটে,0,sports
মুশফিক কে যে তাকে গালি দিলে একজন সাধারণ মানুষকে এমন মানহানি করতেছেন। আমি ঐ দর্শক ভাই কে বলছি আপনি মাহহানি মামলা করেন।,0,sports
সময় পরিবর্তনের সাথে দাবি তো তুলবেই।,0,sports
বাদদে খেলা,0,sports
মুসফিকের ঐ একই বালের মার দেখলেই আমার শরীর জ্বলে যায়।,0,sports
যদি মুশফিক জাতীয় দলে এইভাবে খেলতেন🙁🙁🙁,0,sports
তোমার মুখে জুতা দিয়ে দেওয়া উচিৎ পাপনদা,0,sports
এরকম একটু ফুরতি তলে তলে সবাই করে।এখন ওরা সেলিব্রেটি তাই ওদের টা ফাস হলেই শিরোনাম হয়ে জায়।সানিয়া মিরজার মত মাল সামনে পেলে যে কোন পোলার ই ধন দারিয়ে যাবে।মেয়ে রা ফুরতি করার ই মাল।খানকিদের মত চলা ফেরা করবো আবার ওনাদের চুদলেও দোশ নাকি??,0,sports
ভাই আমি পাপন সাহেবের এলাকার। তারপর আমি বলব পাপন সাহেবসাকিব ভাইয়ের সাথে কাজটি ঠিক করে নাই। পাপন সাহেব মনে হয় তার পিছনের কথা বলে গেছে।,0,sports
সিলেটকে আমরা ভালো বাসঁ দিতে পারি 😂😂😂😂,0,sports
এই পাপনই সমস্যা,0,sports
টাটা বাই বাই 😎😎 ভালবাসা প্রেম নয় 😭😭,0,sports
পাপন রে জুতা মারি,0,sports
আমার দাবী সাকিবকে চাই,0,sports
শাকিব ↓ আমাকে আপনারা আগের মত সাপোর্ট করবেন। আমি আরো শক্তিশালী💪💪 হয়ে ফিরে আসব,0,sports
নামাজপড়ে আল্লাহতায়ালা কে ডাকি,0,sports
আমার মনে হয় পাপন সাহেব ঠিকই বলছেন।😍তিনি দেশের ক্রিকেটের উন্নতির জন্য সব কিছু করে যাচ্ছেন।তবু ও কেন সাকিবতামিমমাহ মুদুল্লাহ রা এরকম দাবি জানাচ্ছে??? বিষয়টা খুব বেশি করে গবিড়ে যাওয়া দরকার।আমি সত্যি দেশের ক্রিকেটকে অনেক ভালবাসি 🇧🇩😍,0,sports
সাইদ ভাই পাপন তার চেয়ে থাকি বলে না থাক ✌✌👉🇧🇩🇧🇩🇧🇩🇱🇷🇱🇷,0,sports
তাহমিদ অমিত ভাই আমরা সবাই কিন্তু জানি ইতিহাস বলে একটা শব্দ আছে।যুগে যুগে কিন্তু মির জাফর জন্ম নেয় ।আজকের এই হিরু পাপন কাক্কু ।ইতিহাস তোমাকে সাধিন বাংলাদেশের মির জাফর হিসেবে ধিক্কার আর থু থু থু থু দেবে।,0,sports
আমি অনেক হেপি,0,sports
কিসের খেলা সব বন্ধ,0,sports
সম্পূর্ন গেম টা ছিল প্রি প্ল্যান। সো,0,sports
সাকিবের উচিত ছিলো দুর্নীতি করা সেটাই ভালো ছিলো,0,sports
শাকিবকে তারাতারি ফিরিয়ে আনা হক,0,sports
হাহাহাহা,0,sports
আপু তোমার কথা;র জয় হোক সাকিব দূরত্ব খেলায় ফিরুক। কারণ সাকিব যত দিন ক্রিকেটে না ফেরে ততো দিন আর ক্রিকেট খেলা দেখবো না,0,sports
মুশফিক কোন হনু যে ওরে গালি দিলে আহামরি বড় কোন সমস্যা হয়ে যাবে! আমি থাকলে আগেই থাপরাইয়া কান দিয়ে হাওয়া বাইর করতাম।,0,sports
বাংলাদেশে এমন অধিনায়ক আর পাবে না,0,sports
সাকিব না খেলে তাহলে বাংলাদেশ শেষ,0,sports
লোকমান কিন্তু ক্যাসিনো কি জানে না পাপন্দা,0,sports
জারা পাপন কে খারাপ ভাবে তারা ভুল ভাবছেন।,0,sports
এর জন্মের দোষ আছে,0,sports
হ্যাঁ বাংলাদেশে অনেক ভন্ড হুজুর আছে তাই বলে সবাইকে এক কাতারে দাঁড় করানো অনেক বড় মূর্খতা ।আর কারো বক্তব্য পুরোটা তুলে না ধরে তার বিরুদ্ধে সমালোচনা করা আরো বড় মূর্খতা । আপনি গানের কথা বললেন!কোন গানের সুরকে যদি ইসলামী সুন্দর কথার মাধ্যমে প্রকাশ করা যায় তবে সেটা কি খারাপ কিছু?আপনি দয়া করে মিজানুর রহমান আজহারির শিক্ষাগত যোগ্যতা সম্পর্কে জেনে নিবেন।আপনার জ্ঞান কতটুকু আমি জানি না! ডা জাকির নায়েক তার এক লেকচারে বলেছিলেন স্বল্প শিক্ষা ব্যক্তিকে ধর্ম থেকে দূরে নিয়ে যায় কিন্তু সঠিক ও উচ্চ শিক্ষা ব্যক্তিকে ধর্মের কাছাকাছি আনে ।,0,sports
আবার ও এক দুই রানের আফসোস,0,sports
সাকিবকে ছাড়া ম্যাচ খেলতে গেল জুতার মালা নিয়ে আসবে আমাদের টিম এই যদি হয় আমাদের দেশের মানুষেমানুষের অবস্থা তবে আমাদের টিম কি করবে এমনিতেই আমাদের টিম অনেক দুর্বল তার পরও এরা মানুষকে দাবিয়ে রাখার জন্য এতো চেষ্টা কিছু হবে না আমাদের দেশে বাকি জারা আছে সবাইকে বোসে যাওয়া উচিত জানি না একেমন বিচার,0,sports
দুষ্টু গরুর চেয়ে শূন্য গোয়াল অনেক ভালো!!,0,sports
এক কথায় বুঝে নিবেন বাংলাদেশে কোনো মানিক মুক্তার দাম নেই যা বর্তমান শ্বাসক গোষ্ঠীর কারনে,0,sports
জার্সি পরা বরিশাইল্লার কি বিস্রি ব্যবহার এটাই বরিশাইল্লার আচরণ,0,sports
ভাই খেলাই আর দেখবো না,0,sports
রুবেল মিয়া হ্লার ব্যাটিং দেখে মনচাচ্ছিলো কানের নিচে টাস টাসাইয়া কয়টা তাপ্পর মেরেদেই👊,0,sports
ওদের মত ক্রিকেটারদের আজীবন নিষিদ্ধ করা হোক,0,sports
সাব্বির অামার সবচেয়ে প্রিয় খেলোয়ার।<br />এই বয়সে এমন কিছু হতেই পারে।,0,sports
এসব পাপনের চাল বাসে আর কিছু পায়না দেখে এখন সাকিবকে এই ঝামেলায় ফেলতেছে😡পাপন বাংলাদেশের ক্রিকেটকে ধবংস করে দিবে।পাপন সভাপতির পদ থেকে বহিষ্কার করা না হলে বাংলাদেশের আগামী দিন জিম্বাবুয়ের মতো হতে পারে??,0,sports
ইলিশ দিলাম।আর পেয়াজ বন্ধ।বাংলাদেশকে শেষ করে দেবে ভারত।,0,sports
ছাগুদের গা জলা শুরু,0,sports
মুশফিক ভাইয়ের সেন্চুরিটার জন্য আজকে ও অনেক আফসোস লাগলো।,0,sports
রাজশাহী কাপ জিতাতে কে কে খুশি লাইক দিয়ে যাও,0,sports
বিপিএল ফাইনাল ম্যাচে আপনি কোন দল সাপোর্ট করতেন খুলনা টাইগার্স নাকি রাজশাহীর রয়েলস।,0,sports
টা কে ঠিক মতো যত্ন নিলে ভবিষ্যৎ এ ভালো সার্ভিস দিবে। ইন শা আল্লাহ,0,sports
"আমি বলব সাব্বির রে এই প্রথম তাই আমি আব্বার বলছি এইবেপার টা নিয়ে কেছু লেখবেন না,,,, আমি বলব এইতিন টি মেছে কে কত করেছে,,,একবার বাল বাভে দেখিন",0,sports
পাপনের মেয়ে কে দিয়ে খেলাতে হবে,0,sports
পাপনকে দেশ থেকে তাড়িয়ে দিন,0,sports
রাসেলের মুখে ইণশাআল্লাহ্ শুনে অভাক হলাম।,0,sports
সাকিব তো রাজি হয়নি।তবে কেনো শাস্তি।ভুয়া,0,sports
আহামাশরাফির মত প্লেয়ারকে টি থেকে বহিষ্কারনাম দিয়েছে অবসর😭😭😭😭😭ওই আইসিসি যতদিন ইন্ডিয়ার থাকব্রততদিন সাকিব নিষিদ্ধকারণ ভারত আমাদের দু চোক্ষে দেখতে পারে না।,0,sports
খেলা না দেখলে কি হয় ভাই।এরা আবার খেলোয়াড় আফগানিস্তানের সাথে জিততে পারে না।বেশিরভাগ খেলোয়াড়দেরই ব্যবহার খারাপ,0,sports
তাসকীনের গুয়া মার তরা দুইজন,0,sports
মানুষের ভিবেগ যে এতো ছোট ওর কাছ থেকে মেনে নিতে পারলাম না হারামি,0,sports
পাপন নান্নুজুজন পদত্যাগ করা হক কে কে একমত,0,sports
তুর কাজ নাই,0,sports
নাজমুল হাসান এর ভক্ত গুলা হাত তুলো,0,sports
খুব কস্টো লাগছে তুমি চিন্তা করোনা আমরা তোমার পাসে আছি,0,sports
বাংলাদেশ হচ্ছে আগামী দিনের ভবিষ্যৎ,0,sports
ঠিক বলেছেন ভাই সাকিবের মতো এভাবে করা ঠিক হয় না সাকিবের পেছনে কোন হারামি শালা লেগেছে?⚔️❤️এতো সুন্দর অলরাউন্ডার সাকিব ❤️,0,sports
❤আমার মত কে কে ক্রিকেট ভালোবাসেন?💕💕 তারা লাইক করুন 👇👇👍👍,0,sports
পাপনের নামের শেষের অক্ষর বাদ দিলে হয় পাপ যার নামের শুরু পাব দিয়ে তার শেষ পাপ আমরা পাপ মুক্ত বিসিবি চাই,0,sports
আবাল নিউজ,0,sports
এসব ঘটনা বাংলাদেশের ক্রিকেটকে ধ্বংস করে দিতে পারে,0,sports
কোন কারন না খুজে যে ভাবে সমাধান হয়তাকরাই ভাল আমি মনে করি।দেশের জন্যও ভাল ক্রিকেটের জন্যও ভালো।,0,sports
সব ছেড়ে বড় চোর পাপন,0,sports
তুই এতো কথা বলার কে? কথা বলবে নির্বাচক কমিটি।,0,sports
ভাই শাফিনকে কি ছাইড়া দিলেন।,0,sports
ডিপজল ফেইল,0,sports
পাপোন্দার পদত্যাগ চাই।,0,sports
তুমি হারাপ১০০%,0,sports
পা পোন্দা ভাল কথা বলছে,0,sports
সাব্বিরকে দলে নেওয়া মানে বলদামি এছাড়া আর কিছুই না,0,sports
আসসালামু আলাইকুম।।।। সাবাশ ভাইয়া।,0,sports
সাব্বিরকে দলে নেওয়ার বিপক্ষে থাকলে ও উর্যাপন নিয়ে সমালোচনার কিছু খুজে পাই না।,0,sports
বীর ফিরবে বীরের মতই,0,sports
নিজের নামে রিংটোন তৈরি চাইলে ভিডিও টি দেখুন আরো নতুন নতুন ভিডিও পেতে হলে চ্যানেল টি সাবক্রাইব করুন,0,sports
সোনার খেলাই আর দেখমু,0,sports
ভাই আর বাংলার খেলাই দেখব নাসাওয়ার দে‌শে সব‌কিছু‌তেই রাজনী‌তি মা‌গির বেটারা বো‌ঝে না সা‌কি‌বের ম‌তো প্ল‌ে‌য়ার আদৌ বাংলা‌দে‌শে আস‌বে কি না!খুব কষ্ট পাই‌ছি‌কিচ্ছু কমু না শুধু দেইখা যামু!,0,sports
ভাই সেরকম হইলে আমরা সবাই চাইলেই যে কোন খেলোয়াড় এর ওয়াটসএপ নাম্বার যোগাড় করে তাকে ম্যাসেজ দিতে থাকবো ম্যাচ ফিক্সিং নিয়ে। আর আমরা জানি খেলোয়াড় রা ব্যাস্ততার কারণে হউক যে কারণে হউক যে কারো ম্যাসেজ কেয়ারই করেনা। কাউকে জানাবে তো দূরে থাক 😆😆,0,sports
বান্দরের মতে,0,sports
এর দেয়া বন্ধ করে দেওয়া হলো কেন???,0,sports
জার্সি পরা স্যামসাং তুই তো একটা বেয়াদব গাঞ্জুট্টি তোর মুখের দিকে তাকালেই বুঝা যাচ্ছে গাঞ্জুট্টি,0,sports
বাংলাদেশ এর ক্রিকেট এর একমাত্র শত্রু ভারতআর এই ভারত আপনাদের বন্ধু,0,sports
"ভাই আপনারা নিজের দেশের সম্মান রাখতে জানেন না। এতোদিন তো এই কথা বলেননি। এই চ্যানেল হয়তো দেশি বিদেশি অনেকে ফলো করেন।তারা কি ভাববে? কার সম্মান যাবে? আপ্নারা এতো কিছু বুঝবেনন না, কারন আপনাদের চাই ভিউ। দেশের সম্মান, ক্রিকেট বোর্ডের সম্মান আপনাদের কাছে বড় না। যারা এই কমেন্ট পুরোটা পড়ছেন তাদের ধন্যবাদ। আমি কিন্তু সাব্বির কে সাপোর্ট করতেছি না। কারন সে অপরাধ করছে। আপনারা এই খবর ৬ মাস আগেও প্রকাশ করতে পারতেন। কিন্তু তা করেননি। এখন মনে করছেন এই খবর এখন দিলে পাবলিক মজা নিবে? তাহলে আপনাদের ধারনা ভুল।দেশের অভ্যন্তরীণ খবর দেশেই রাখেন। যেগুলো প্রকাশ করার সেইগুলো করেন।<br /> আর কয়েকটা প্লেয়ার তো আছেই বাংলাদেশ টিমে। চরিত্রহীন।",0,sports
বাংলা বলা টা লজ্জার না গৌরবের কারণ এই বাংলা ভাষার জন্য রক্ত দিয়েছ সালাম রফিক জব্বার বরকত তাদের রক্তের বিনিময়ে পেয়েছি আমাদের প্রিয় বাংলা ভাষা আমাদের মায়ের ভাষা তাই সবার তাদের মায়ের ভাষার প্রতি শ্রদ্ধাশীল থাকা দরকার ।,0,sports
আমার তা চাইলে ঘুরে আসতে পারেন😐,0,sports
সাকিব ছাড়া এ দেশে কোন ভালো খেলোয়ার নাই,0,sports
মজা পেলাম,0,sports
😜,0,sports
অামার কল ধরছে.অামার সাথে কথাও বলছে/./,0,sports
মিরাজের খেলা ভালো লাগছে কার কার👇👇,0,sports
সাব্বিরই ঠিক আছে,0,sports
ভারত সফর কেমন করে সেটা আগে দেখি পরে কমেন্ট করুম,0,sports
নিজের নামে রিংটোন তৈরি চাইলে ভিডিও টি দেখুন আরো নতুন নতুন ভিডিও পেতে হলে একটা চ্যানেল টি সাবক্রাইব করুন,0,sports
পাপনকে বাদ দিয়ে অন্য কিছু করা ঠীক,0,sports
ঠকবাজ কইএক দেখাই আরেক,0,sports
জিতলো রাজশাহী দেখলো দেশ,0,sports
যারা যারা নানকের সিগারেট ফুকা দেখতে চান তাদের জন্যে 🤣,0,sports
সাকিব যেনো না ফেরে। কারন নিজের দেশ থেকেয় মন উঠেগেছে।অনেক কষ্ট লাগলো সাকিব ভায়কে বহিসকার করে।আর পাপন ওই জুয়ারিকে জুতা মারতে মন চায় কিন্তু কাছে পায় না তো।।।তবে সাকিব ভায় দেশের হয়ে আর খেলেন না।। পারলে এবার থেকে ঘুষে খেলেন যখন নাম উঠায় দেছেয় তখন আর ঘুষ নিতে সমস্রা কি।।।শুভ কামনা সাকিব ভায় আপনার পাশে সারা বাংলাদেশের লোক আছে।,0,sports
পাপন সালা গুরু,0,sports
খুলনার সাপোর্টার রা লাইক দাও,0,sports
যা মারল বিদেশিরা বাংগালীরা মারতে পারেনা,0,sports
রুবেল খুব চালাক?,0,sports
গান কোথায় রে আবাল?,0,sports
ভাই আপনি খুব কথা সুন্দর বলছেন।<br /> আমি আপনার সাথে একমত।<br /> সাধারণ জিনিসগুলো যে কেন মানুষে বাঁকা-ত্যাড়া করে দেখে আল্লাই জানে।<br /> মানুষের চিন্তা ধারণা কবে যে চেঞ্জ হবে ভাবনা তেই আসে না। আপনার কথাগুলো ভাল লাগল। ধন্যবাদ,0,sports
যারা দেখেন তারা আমার থেকে ঘুরে দেখবেন।,0,sports
বাংলাদেশ ক্রিকেটে অনেক রাজনীতি হচ্ছে,0,sports
এইডা কি করলো 🙄🙄,0,sports
সাকিব মিস ইউ,0,sports
সবাই মিলে পাপন কে জুতা মারা দরকার,0,sports
এটা কি ভাষা? জাতীয় দলের ক্রিকেটার এরা? ছি ছিঃ,0,sports
ভাই যারা মানসিকভাবে খুন হয় তাদের বিচার করে আর যারা খুনী তাদের কোনো বিচার করে না ?,0,sports
😰😰সাকিব ভাইয়া যেদিন খেলবে সেদিন আমি ক্রিকেটে খেলা দেখব আর নিজের দলকে ভালো বাসব😭😭,0,sports
ওহ্ পাপনের বক্তব্যে এটা ক্লিয়ারভারতের সঙ্গে খেলা তাই সাকিব,0,sports
এইজে অচেনা মানুষ ভুল করেও ভেবো না যে মুস্তাফিজ আবার আগের মতো হয়ে যাবে 🤓😁😀,0,sports
বালের খবর,0,sports
"সাব্বিরের উদযাপন টা ভুল কি ছিলো,, সমালোচকদের জবাবটা সঠিক ছিলো",0,sports
"সাব্বির কোন প্রকার অভদ্রতা করেনি। কারণ এটি তার প্রথম সেঞ্চুরি, তাই এই উল্লাসটাতে তার কোন অভদ্রতা হয়নি। মাশরাফি চার পাঁচ বোতল সমানে মেরে দিছে মেবি। তাই ওর মাথা খারাপ হয়ে গেছে।",0,sports
তোর বাপের কি,0,sports
ওরা চাইবো কেন তোর কাছে? তুই বিসিবি প্রেসিডেন্ট হয়ে কি বাল ফালাস। তোর তো খেয়াল রাখা দরকার ছিল ক্রিকেটারদের ফিসিলিটিস নিয়ে।,0,sports
ইনশাআল্লাহ্‌ বলাতে ধন্যবাদ এন্ড রাসেল কে,0,sports
এক জন আরেক জনকে আঘাত করে এইটা কোন ধরনের ফান ভাই 🤔🤔 এরা তিন জন ছাগলের তিন নাম্বার বাচ্চা,0,sports
ছোট বেলা থেকেই খেলাধুলা খুব পছন্দ করি ক্লাস মিস হলেও আমার কোন খেলে দেখা মিস হয় নাযদিও আমি মেয়ে যখন এই খবর শুনলাম খুব খুব কষ্ট কান্না পেয়েছে অনেক প্রশ্ন ছিলো কখন কেন কারা এমন প্ল্যান করছিলো দুই বছর আগেই আজ প্রমাণ ছাড়া কিভাবে এতো বড়ো একটা পদত্যাগ করলযেসব প্রশ্ন গুলো আপনি করলেন ঠিক এই প্রশ্ন গুলোই কিছু পোস্ট করেছি কিন্তু কয়জনের সামনে তুলে ধরা হবে আপনার কথা গুলো শুনে মনটা খুব হালকা হলো ভাই ধন্যবাদ। দুইটা বছর পিছিয়ে যাবে আমাদের দেশ।😢😢,0,sports
সাকিব ভাইয়ের ভক্তদের দেখতে চাই❤❤,0,sports
ওরা শুধু বাংলাদেশ ক্রিকেট এর দূর নাম করেনি করেছে বাংলাদেশের দূর নাম করেছে ওদের এখনি ছেটে ফেলা উচিত...,0,sports
সাবধান ছেলেটাকে ছেড়ে দেওয়া হক।,0,sports
টিপু ভাই আমি আপনার ভিডিও সব সময় দেখি কোনো দিন কমেন্ট করিনাই আজ করলাম কারন এই পাপন হারামির বাচ্চা তাকলে ক্রিকেট ধংস হইয়ে যাবে সালা হারামি পাপন একটা জুয়ারি হারামিকে পদত্যাগ করতে কে কে আমার সাতে আছেন 😂😂😂😂😂❤ইউ শাকিব❤মিস ইউ শাকিব,0,sports
তর থেকে আমরা শিখমু তুই বারবার মতামত জানতে চাছ পাগল,0,sports
গরীব বেয়াদব মদ খায় সালারপুত মদ না খাইলে তোগো বুদ্ধি হইবো না।,0,sports
দেশের ক্রিকেট ধ্বংসের পথে।,0,sports
"সাব্বির সেঞ্চুরি করেছে এই রকম উদযাপন করাটাই তো স্বাভাবিক | ভেবে দেখেন সাব্বিরকে নিয়ে যারা সমালোচনা করেন,তার জায়গায় যদি আপনি সেঞ্চুরি করতেন তাহলে কি পীর বাবার মত এক জায়গায় বসে থাকতেন, না তার চেয়েও বেশি সেলিব্রেশন করতেন | সাব্বিরকে নিয়ে যদি এতই সমালোচনা তাহলে খেলা থেকে তাকে বাদ দিয়ে দেন | সাব্বির ব্যান্ড হয়েছে তা নিয়ে সমালোচনা, সাব্বির রান করতে পারে না তা নিয়ে সমালোচনা, সাব্বির সেঞ্চুরি করেছে তা নিয়ে সমালোচনা, তাহলে সে করবে টাই কি | মানুষ মাত্রই ভুল, সে তার ভুল স্বীকার করেছে, এবং সেই ভুলের প্রায়শ্চি ও পেয়েছে| তারপরেও কেন তাকে নিয়ে এত সমালোচনা, ক্রিকেটের জন্মের পর থেকে এখন পর্যন্ত অতীতে যারাই প্রথম সেঞ্চুরি করেছে এর চেয়ে অনেক অনেক বেশি সেলিব্রেশন করেছে, কই তাদেরকে নিয়ে তো কেউ এত সমালোচনা করতে দেখি নাই | অন্যের সমালোচনা করার আগে নিজের ব্যাকগ্রাউন্ড দেখেন, আমি নিজে কি??? আশা করি আপনার জবাব আপনি নিজেই পেয়ে যাবেন",0,sports
মুশফিক তোদের বাপ।।গালি দিয়েছে তো কি হয়েছে।।মোশফিকের এমন আচরনেই বলে দেয় কোন পরিবারে ওর জন্ম।।,0,sports
সঠিক সিধান্ত।,0,sports
আবাল সব সিজদা দেওয়া দেখেন নি????,0,sports
সাব্বির ভাই তুই সেরা তুই পারবি,0,sports
সব সহ্য করতে হবে!,0,sports
এক কথায় প্রকাশ পাপকে করেন যিনি আপন তিনি হলেন পাপন,0,sports
নতুন একটি নাটক সবাই দেখবেন প্লিজ চোরের নেতা জয়নাল,0,sports
ভাই আপনি আত্মহত্যা করে আপনার আত্নাকে মুক্তি দিন। আপনার আত্না আর আর এই অপমান সহ্য করতে চায় না।সে আপনার থেকে মুক্তি চায়।,0,sports
সান্টোকিরে আনছে বিপিএল এর বদনাম করতে। 😂,0,sports
খুব সুন্দর কথা বলেছে ভাই,0,sports
খেলা হবে খেলা হবে,0,sports
বাংলাদেশের খেলাদেখা ভোলে গেছি নাড়ের ছাবাল গের জন্য দেশের বদনাম,0,sports
সাকিবুল হাসান নিষিদ্ধ করছে ইন্ডিয়া লগে কি পাপন খেলবো ইন্ডিয়া প্লেয়ার তিন কোটি বেতন তিন কোটি টাকা বেতন বাংলাদেশ প্লেয়ার তিন লাখ,0,sports
মনে হচ্ছে মশাই অনেক কষ্ট পাইছেন। কিন্তু কথা হলোআপনি তো তাদের ছোট ছোট দ্বাবী গুলোর ব্যাপারে কিছুই বললেন না। ওনারা ন্যাশনাল টিমের বাইরের খেলোয়াড়দের নিয়েও বলেছেআর আপনি সেসব ব্যাপারে না বলেই কেবল নিজেকে সাধু প্রমানের চেষ্টা করলেন৷ বস্তুতসত্য সম্ভবত এটাইওনারা আপনাকে আর চায় না। দ্বাবীর পিছনে আসল রহস্য এটাই।,0,sports
আমি খুব অবাক হই যখন দেখি টেষ্ট একাদশে ইমরুল কায়েস নাই।,0,sports
আমাদের জনগণের আবেগের কোন দাম নেই এ সরকারের কাছে। আবরার সহ আরও কত কিছু দেখলাম কিছু হয় নি হবেও না।,0,sports
রাসেলর কারনে জিতলো রাজশাহী। রাসেলর ভক্তরা লাইক দাও।,0,sports
জাতীয় দ‌লের প্লেয়ার হ‌য়ে এধর‌ণের পাগলা‌মি তাঁর মানায় না। হাস্যকর।,0,sports
এখন কি সম্ভব না আপিল করাবা শাস্তি কমানো?,0,sports
কথায় কথায় যে সাংবাদিকরা বলে কোহলির বেতন কোটি টাকাস্মিথের রুটদের বেতন লাখ ডলারআমাদের প্লেয়ারদের বেতন এত কম কেন? আরে বেটা কোহলির মত পরপর তিনটা ডাবল সেঞ্চুরি করে দেখা নাস্মিথের মত টেস্ট খেল কোটি না কোটির বাপ ও দিয়ে দিবে তোমাদের। রান করবা আর টাকা লাগবে লাখ? ফাইজলামির ও একটা লিমিট থাকা উচিত। বলে রানটা যেদিন করতে পারে নাইসেই বছর পুরাটা বেতন বন্ধ রাখা উচিত ছিল। 😡😡,0,sports
মুশফিকের উপরে এখানেও অভিচার ! নিজের দেশেও শান্তি নেই 🤔🤔,0,sports
বাংলাদেশতো অনেক আগেই শেস হয়ে গেচেকিন্তু এবার ক্রিকেট খেলাটাও গিলো😭😭,0,sports
খেলা জমবে না ফাইনালে যদি চিটাগাং জিততো তাহলে খুলনা চিটাগাং ভালো খেলা হত নিচিত এখন খুলনা জিতবে,0,sports
পাপন সাহেব যে কথাগুলো বলেছেনসবকটি কথা যুক্তিসংগতবাংলাদেশের ক্রিকেট কে ধ্বংস করার জন্য কিছু খারাপ মানুষ উঠে পরে লেগেছে।পাপন সাহেবের কথায় ক্লিয়ার বোঝালাম বিষয়গুলো আসলে কি !,0,sports
আচ্ছা? ইউটিউবে কী অটোডিসলাইক আছে নাকি? নয়ত এরকম ভিডিওতে এত ডিসলাইক আসে কোথা থেকে? 🙄,0,sports
মজা লাগলো,0,sports
হাসু আপুর মতো ওর সব নেতারা গুদির নিচে ফেবিকল আঠা দিয়ে বসে আছেযতই মানুষ পদত্যাগ চায় না কেন এরা পদত্যাগ করবে না সবগুলো তো হাসু আপু চামচাগরু যেমন শিষ্যকে শিক্ষা দিয়েছে শিষ্য তো সেটাই শিখবেতবে এটা ঠিক হাসু আপু সহ সব নেতারা যদি অভিনয়ে কাজ করতো এতদিনে বাংলাদেশ বলিউড থেকে ভালো উন্নতমানের ছবি দেখতে পারবো 🐸🐸🐸,0,sports
সোনার ছেলেদের মুখের দিকে তাকান এদের অবস্থা কি সুধু বিসিবি কারনে,0,sports
খেলোয়াড় আর রা এ রকম হয় ছি একটা মেয়ে বিশ্বাস ও সম্মান এবং ভালোবাসা সকল কিছু কে ভেঙ্গে দেয় এব়ং একজনের জন্য সার বাংলাদেশ সম্মান যায় এই নাকি বাঙ্গালী জাতি,0,sports
ম্যন অবদা ম্যেছ ম্যন অবদা সিরিজ দুটাই আওয়ামিলিগের কাজের মত হোইছে।পুরা খেলাতো আমিলিগের মত হোইছে পাইনাল টাও একি রকম হোইছে। আপছুচ মুশির জন্য,0,sports
পাপন হল মূল নাটের মুল। কারন এতদিন পরে কেন বিসিবি একশ্যান নেয়। শাকিবের ওপর রাখ জারল।,0,sports
বালের খেলা মানুষ এখন ওয়াজ নিয়ে আছে মানুষ আর আগের মতো বোকা নাই,0,sports
শুধু দুঃসময় নয় বস সবসময় তোমার সাথে ছিলাম সাথে আছি থাকবো ইনশাআল্লাহ।। ভালোবাসা বস শুধু ভালোবাসা তোমার জন্য।,0,sports
মেসি নেইমারের মতো বিশ্ব মানের প্লেয়ারদের জুতা ডিল মারে তাও কিছু হয়না আর সামন্য গালি দিয়েছে তাতেই এতোকিছু আমদের মন কতো নিচু ছিঃ ধিক্কার জানাই এদেশের মানুষের মনুষ্যত্বকে।।,0,sports
রিং আইডি দিচ্ছে নতুন বছরের নতুন ধামাকা নতুন রেজিস্টার করলেই টাকা বোনাস সেই টাকা বিকাশ অথবা রকেট দিয়ে তুলে নিতে পারবেন রেজিস্টার করার সময় রেফার কোড হিসেবে ব্যাবহার করবেন এই কোডটি না হলে টাকা পাবেন না কোডটি রেফার করে লগ ইন করলেই বোনাস পেয়ে যাবেন। ধন্যবাদ,0,sports
পাপনরে কচ্ছি তুই মাঠে নাইমে খেলে সেঞ্চুরি কইরে কথা ক টুট,0,sports
খুবই চমৎকার খেলেছে মুমিনুল হক।,0,sports
নাম্বার ওয়ান সাকিব আল হাসান।,0,sports
আরে পাপন সাহেব গাজা খাইছেন নাকি?,0,sports
কোন কোন বোকাচোদা মিলে ম্যান অব দ্যা ম্যাচ নির্বাচন করছে।।,0,sports
বাংলাদেশে কি ছেলের অভাব যে এই নিগরু টাকে নিয়ে মেয়েরা স্বপ্ন দেখে,0,sports
এতদিন কি করছে ক্রিকেটদের দাবি আন্দোলনের জন্য নেতৃত্ব দেওয়ার কারনে বোর্ড সভাপতি পাপন সাহেব তার পিছনে লাগছেঅবশেষে বলবো পাপন সাহেব সাকিব পৃথিবীর যেকোনো দেশে খেলার যোগ্যতা রাখে তার পিছনে না লেগে পদত্যাগ করেন আপনি বাংলাদেশের জন্য কিছু দিতে পারেন নাই।,0,sports
চোরের কমিটি।,0,sports
রুবেল একটা খারাপ ছেলে চি চি এরকম চেলে যেন আর কারো ঘরে জন্ম না নেয় হি রুবেল কি সুদশন পাএ তার জন্য মেয়ে র পাগল ফালতু,0,sports
জিতবে এইবার চট্টগ্রাম দেখবে সারা গ্রাম । ভালবাসা রইল চট্টগ্রামের প্রতি ।,0,sports
রুবেল কার কার ফেবারিট লাইক দিন,0,sports
সাব্বির ভাই আমার প্রিয় খেলোয়াড়!🇧🇩,0,sports
পাপনকে নিষিদ্ধ করা হক,0,sports
ছি ছি ছি ছি এত খারাপ চামচা গুলা বিশেষ করে জার্সি আলা,0,sports
পাপনের উপর রেট করা উচিৎকে কে মনে করেন এটি👌👌,0,sports
নামাজ পরো কে কে লাইক দেও নামাজ জাননাতের চাবি,0,sports
জাতীয় দলে জাতীয় বেয়াদপ প্লেয়ার 👈👈,0,sports
"সাব্বির লাইভ সেক্স ভিডিও লিন্ক, বাচ্ছারা আসার দরকার নেই,, <br /><a href=""https://youtu.be/VJiZJ_nhwhc"">https://youtu.be/VJiZJ_nhwhc</a>",0,sports
পাকিস্তানি ক্রিকেটারদের জন্মই যেনো সবসময় অবস্থার বিপরীতে অবিশ্বাস্য কিছু করে দেখানোর জন্য,0,sports
চোর চোর খালাতো ভাই,0,sports
অসাধারণ ভাইয়া,0,sports
সিকিউরিটিদের কোন যোগ্যতা আছে সালা গো,0,sports
নতুন একটি নাটক দেখবেন,0,sports
আমি আর খেলা দেখবো না,0,sports
তবে নতুনদের সুযোগ দেওয়া হোক।,0,sports
খেলা দেশের জন্যে খেলছে টাকা নিয়ে টানাটানি করলে রেংকিং টেস্ট তে নাম্বার আর ট তে ও ।। ভালো খেললে টাকা আপনা আপনি টাকা আসবে টাকা দিবে। দেশ তাকিয়ে থাকে ক্রিকেট কে। এখন দেখছি ফুটবল কে সাপোর্ট করতে হবে।,0,sports
পাপনের পদত্যাগ চাই।কে কে একমত❤,0,sports
পাপনের পদত্যাগ চাই কোথায় আছ বাংলার ছেলেরা জেগে ওঠ,0,sports
এতে করে সাকিবের লাভ হলোকারণ সাকিব জানে কার ইশারায় কল কাটি নড়ে আমার প্রশ্ন হলআইসিসি দুই বছর কোথায় ছিল নাকি পাপইননা হালার বিরুদ্ধে যাওয়ায় এটা এখন সামনে এলআর কত দুই নাম্বারি করবিসব কিছু একদিন প্রকাশ হবে,0,sports
আমি মনে করি এই সুপার ওভার এ জয়ের নায়ক মজিব উর রহমান জাদরান,0,sports
আই ছিছির মন গড়া সাকিবকে বাদ দিলে হবেনা বাংলাদেশের কোট লাক হাজার সত জন লুক রায় দিবে সাকিব পতি ম্যছে খেলতে হবে আইছিছি রায় আমরা মানিনা,0,sports
পাগল যে আপনারা পৃরমান পাইলাম।।।আজাইরা ক্যাপশন আর আজাইরা ভুয়া নিউজ।।,0,sports
অনেক খোতি হবে,0,sports
কষ্ট পেলাম,0,sports
বিসিবিকে আরো কঠোর হতেহবে,0,sports
পাপন টাকা মেতরেও কামায় মনে রেখো তোমি,0,sports
আফসোস জিম্বাবুয়ের মত হতে চলেছে,0,sports
যারা একানে এসে আ বাল মারকা ভিডিও দেখে সাকিবের বিষয়টি সত্য ভাবতেছেন এবং ইমসনাল কমেন্টে করতাছেন। তাদের জন্যেই এই ধরনের ভিডিও বানিয়ে থাকে।,0,sports
এই শামীমরে দেখলে কেমন বিরক্ত লাগে।ধারাভাষ্যকে এই বেটায় বিরক্তিকর পর্যায়ে নিয়া গেছে।,0,sports
ফুটবল প্লেয়াররা আর বড় সমস্যায়,0,sports
এটা মোটেও ভালো হয়নি তাসকিন তুমি কাজটা ভালো করো নি তোমার তাদেরকে মিলিয়ে দেওয়া উচিত ছিল,0,sports
এটার নাটক করে ও কান্না করছে,0,sports
কোন কথা নাই পাপন পাপির পদত্যাগ চাই,0,sports
হারিয়ে যায়েননা ভাই ফর্ম ধরে রাখেন।জাতীয় টি দলে জায়গা করে নিন।,0,sports
বাংলা বলছে এজন্য আমার খুব ভালো লাগছে,0,sports
"টোকাই এর বংশধর,,,,🎇",0,sports
এটা পাপন স্যারের গভির সরজন্ত,0,sports
ফারুক শেষ,0,sports
আঁরার চট্টগ্রাম এবারের টিম কম্বিনেশনটা ভালো হইছে,0,sports
এটা যদি সত্যিই নাসির হয় তাহলে গেলা থেকে বহিষ্কার করা উচিত,0,sports
পাপন কে চাই না কোটি মানুষের দাবি,0,sports
এবার কেনো বিপিএল কে বঙ্গবন্ধু কাপ রাখা হল????? জানাবেন,0,sports
পাপকোনের গালে গালে জুতা মারো তালে তালেসালা থাক গালি দিলাম না সবাই বুঝে নিবেন,0,sports
সাব্বিরের নাম্বারে ট্রাই করলাম মালয়েশিয়া থেকে কল তো ঢুকে না😂😀<br />+8801743505079,0,sports
সিলোটি পুয়া তাইনেরা আইজখা দেখায় দিলো। তারা এতো দিন মাততাম পরে নাই। আইজকা মাতিয়া লাইছে খিতা খও সিলোটিরা ??,0,sports
পাগল সবাই,0,sports
আমার দোয়া রইলো মুশফিকুর রহিমের জন্য তার দল যেনো চ্যামপিয়ন হয় শুভকামনা,0,sports
রুবেলের ভাষা শুনে মনে হচ্ছে বস্তির ছেলে।এ দেশের সরকারের প্রতি এটাই জিজ্ঞাসা কেন এখনো এরা জাতীয় টিমে খেলতে পারছে।বা খেলতে দিচ্ছে?,0,sports
"রুবেল কে সবাই গালাগালি দিতেছে<br />,,,আর নাসির যে কাজ করতেছে প্রমান সহ সুবা বলতেছে,,,, সেটা কেও মানতে নারাজ<br />,,,সবার কাছে সুবা খরাপ নাসিরের কোনো দোষ নাই,,,,, আপনারা নাসির আর সুবার সব গুলা কল রের্কড গুলা শুনুন তার পর বলুন,,,,, খালি রুবেল না,,, নাসির,, সাব্বির ওদের কথাও বলুন,,,,, কেনো এক জনকে গালি দিবেন",0,sports
সব ছাগল উগলুফুগলো,0,sports
আওয়ামী লীগ বলে কথা এত বড় চালবাজ সিনেমাকে হার মানায়।,0,sports
বাংলাদেশের এই জয়টা একমাত্র আল্লাহর রহমত ছাড়া আর কিছুই না।,0,sports
আজ পাপন সাহেব তার ক্ষমতা দেখালেন ক্ষমতা সবসময় থাকবেনা এটা উনার বুঝা উচিৎ সময়টা সাকিবের ও আসবে সময় কথা বলবে।।,0,sports
কিপিং জাকের আলী অনিক ভাই যে এত সুন্দর ক্যাচ নিলো কেউ তার কথা বললেন না,0,sports
ওদের বল মদ খেতে,0,sports
পাপন শালা বাবুএখানে শুধু টাকার কথা বলা হয়নি,0,sports
এই চাঁমচামির কারনেই দেশের আজ এ অবস্থা হাজার হাজার কোটি টাকা খরচ হচ্ছে উদের পিছনে কি এমন উন্নতি হচ্ছে খেলার মান একজন দর্শক না হয় রাগের মাথায় কিছু বলেফেছে তার জন্য চাঁমচা গুলো কি শুরু করেছে মন ডায় চায় চাঁমচা গুলো কে জুতা পিটা করি,0,sports
সাকিবের ভাইয়ের চেহারা দেখে মনে হচ্ছে না পাপনদা সত্য বলছে শালা একটা বানচোদ,0,sports
সবাই তো পচাইতেছেন সামনে পাইলে তো বলবেন..ভাই সেলফি সেলফি,0,sports
ফাস্ট কমেন্ট নাহিদ ভাই অসাধারন বর্ননা। ভালোবাসা অবিরাম।,0,sports
আজ সাকিব আল হাসান থাকলে হয়তো খেলাটা আরো অনেক সুন্দর ও ভালো লাগতো।আজ হয়তো গ্যালারিটা ফাঁকা থাকতো না। 😥😥😥😥😥,0,sports
আমার চাই পাপন পদত্যাগ করুক,0,sports
ভাই দিপক আগারয়াল কোতায় ওর কি সাস্তি হয় নাই,0,sports
বাংলাদেশের জার্সি পরা ছেলেটার দৈনিক তিন টোপলা গাঞ্জা লাগে আমি ওরে চিনি রুবেলরে বহুতবার গাঞ্জা আইনা দিছে। ও খেলোয়ারদের গেটের সামনে সবসময় থাকে চামচামি করে তাদের।,0,sports
সাকিব আল হাছান ভারত সফর,0,sports
👍👍👍 💥💥 বাংলাদেশে আরও উন্নতমানের স্পিনার তৈরি করতে হবে।।,0,sports
বিনা ভোটের এমপিবিনা ভোটের সভাপতি হলে এভাবেই কথা বলে। সালাউদ্দিন যেভাবে ফুটবল ধ্বংস করেছে পাপন সিন্ডিকেট করে ক্রিকেট ধ্বংস করেছে।,0,sports
পাপন জনগন বোকা পাওনাই তোমার কথা সব ভোকাজ তোমারে দেখলেই বঝাজায়,0,sports
মাদরচুদকে ভাত দাওয়া হোক,0,sports
সুনার খেলা বন্দ হলে ভাল এত সব টাকা দেশের অপচয় করার চেয়ে গরিবদের মাজে দিয়াদে,0,sports
সহমত তাহমিদ ভাই,0,sports
একটু হলুদ একটু মরিচ রোস্টটা হয়নি কড়াকারণ পিঁয়াজের দাম এখন বাড়া। 😂😂😂তাহসীন ভাইকে নিয়ে একটি গান আপ্লোড করেছি আমার চ্যানেলে,0,sports
পাপন নিজেতো জুয়া খোর। জুয়াখোর এখনো বিসিবির সভাপতি কেনো।,0,sports
ভালো লাগে এবং তাকে দলে চাই,0,sports
জানোয়ার তোকে অবিলম্বে ফাঁসি দেওয়া হবে,0,sports
পাপোন্দা কে টুট টুট,0,sports
খেলার মধ্যে রাজনীতি চুদালে এমনই হয়,0,sports
দুয়া তুলসী পাতা।পাপন ভাই,0,sports
অর নুনুটা কেটে ফেল,0,sports
ভাই এতদিন জানতাম সব জায়গায় দুর্নীতি আছে কিন্তু এবার বাংলাদেশ ক্রিকেটের ভিতরেও দুর্নীতি আছে মাননীয় প্রধানমন্ত্রীর কাছে আমার অনুরোধ রইলো শুধু আমার একার না সারা বাংলাদেশ ক্রিকেট ভক্তদের এটাই দাবি সাকিব আল হাসানকে ফিরিয়ে আনা হোক আর যারা সাকিব আল হাসানকে ফাঁসিয়েছে অপবাদ দিয়েছে তাদের বিরুদ্ধে সঠিক এবং ন্যায্য তদন্ত করা হোক,0,sports
রাজনীতির খেলাধুলা বাংলাদেশে চলছেই।বোরহানউদ্দিনের ঘটনাবলী এবং আবরার হত্যা কান্ডের সমাপ্ত এখানেই হবে? নতুনের জন্য অপেক্ষা করুন।,0,sports
টা কাসরা,0,sports
আজকে থেকে আর বাংলাদেশের খেলা দেখবো না।,0,sports
শুনার খবর কয় থেকে পাইছত???😫😫😫,0,sports
পাগল কোথায়কার দুজনকে একটা চেক দিচে,0,sports
হাই,0,sports
ভাই কুছু আরবি গালিদেন,0,sports
কোন সালা বাবা,0,sports
সাকিব না খেললে পাপন বাস খাবে,0,sports
সালে কে কে দেখছেন হাত তুলুন?,0,sports
আপু তুমি আমাকে বিয়ে করবা আমি ডুবাই থাকি তোমার মোবাইল নামবারটি দিবে আমাকে পিলিজ,0,sports
"আপনি সত্যের মুখোশ খুলে দিয়েছেন। ধন্যবাদ আপনাকে,তাছাড়া আপনার প্রকাশ ভঙ্গি চমৎকার",0,sports
পাপনসুজন যতদিন পদত্যাগ না করবেততদিন খেলা বন্ধ হোক।এই চোদনা গুলার খেলার কিছু বুঝেনা।সুজন তো ক্যাসিনো খেলে বিদেশে।,0,sports
বলদ মিডিয়া অর নম্বর পাবলিশ করার কোনো মানে আছে??,0,sports
সাকিব না থাকলে বাংলাদেশ খুব ভাল করেই জিতা ম্যাচ হারে 😃😃,0,sports
কেউ বলে আমেরিকায় চলে যাচ্ছে কেউ বলে ইংলেন্ড যাচ্ছে কতটা সত্য জানিনা???,0,sports
আমরা পাপনের পদত্যাগ চাই। আর কে চান?,0,sports
ফফন,0,sports
পনের জনের কথা বলে লাভ নাই তোসবার কথা ভাবতে হবে,0,sports
আমি অবাক হচ্ছি যে ;একটা সনামধন্য চ্যানেলের নিউজ হেডলাইনের ভাষা এত নিম্নমানের ক্যামনে হয়!;। দালালের বাচ্চারা পাপনের পিছে লাগছেপারলে বড় বড় চোরদের পিছনে লেগে থাক। ক্রিকেট না থাকলেও এদেশের মানুষের কিছু হবেনা। কিন্তু ওসব চোররা থাকলে একদিন দেশ ই থাকবেনা। পারলে ওদেরকে নিয়ে নিউজ কর। তোমরা তা পারবানাখালি পার দালালী করতে 😏😏😏,0,sports
ভালোবাসা অবিরাম সাকিব ভাইয়ের জন্য,0,sports
এতোদিন তারা বাছিঁড়েছে? এটা ষড়যন্ত্রের অংশ!,0,sports
এই জে ভাই আমার কমেন্টার উঃ চাই সেই কি চোর মনে হয়ে তা না হলে তাকে চোর মতো দরে রাখিলো কেনো,0,sports
সাব্বির কে ধন্যবাদ,0,sports
বর্তমান সময়কালে আন্দোলনের ছয় দফার একটি কথা ছিল খেলার আগের দিন হার জিৎ জেনে যাচ্ছি দুঃখ করে বলতে হচ্ছে সাকিব বোকা নয় অনেক বেশি সৎআর এমন সততা আই সিসির নিয়ম কানুনের বাহিরে পারিবারিক রাজনীতি খেলাধুলা যাইহোক না কেন কিছু বিষয় গুপনীয় থাকে যে বিষয়গুলি আপনার জনসম্মুখে প্রকাশ করা সততা নয় বোকামি সাকিবের এই কথাটি ট্রাম্প কার্ট হিসেবে ব্যবহার করেছেন ক্রিকেটের হর্তাকর্তারা (বিসিবি এবং আই সিসি ),0,sports
এই লোকটা ক্রিকেট টা ধংস করে ছাড়বে,0,sports
শুভ কামনা তোমার জন্য,0,sports
এটা হলো,0,sports
সালায় বাইরাল হইতে আইছে,0,sports
এই ম্যাচ গুলায় মজা নাই এক পেসে ম্যাচ,0,sports
সাকিব্বাইয়ের পাশে অাছি❤,0,sports
এটা ঠিক না তোরা দুই জনে মিলে তাসকিনকে মারো,0,sports
সাকিব ভাই আমরা তোমার সাতে আছি,0,sports
কাজের বেটারে দেখলে আবার পাগল হয়ে যায়।,0,sports
যতো দ্রুত সাব্বিরকে জাতিও ক্রিকেট থেকে বাদ দেওয়া জাই।।।,0,sports
চামচামি খুব ভালোই চলতেছে,0,sports
"আসলে কি বলবো ভাই ,আপনার কথা গুলো খুব ভালো লাগছে।",0,sports
সাকিব আল হাসান আমার জান বাংলার জান সারা বিশ্বের জান,0,sports
এই ছেলের জায়গাই যদি আমি হতাম ঐ ছেচরা মানুষ গুলার ওপর অনেক গরম হয়ে যেতাম। টাচ করার সুযোগ দিতাম না।,0,sports
পাগলের দল,0,sports
মুসফিক ভাই পুরো টুনামেন্ট ভালো খেলেছে এবং কি তার কেপ্টেন টা অনেক ভালো করেছে রাসেলের ছেয়েও তাই কিছু পুরুস্কার দেওয়া দরকার ছিলো,0,sports
এগিয়ে যাও,0,sports
শাকিব ষড়যন্ত্রের শিকার আমরা সব বুঝি এইগুলা ইন্ডিয়ার চাল পাপন দালালি করেছে ।।,0,sports
এক সময় থেকে উঠে আসে,0,sports
আউট হইছেন ত কি হইছে সম্মানের সাথে মাথা উচু করে যান বোঝাইতে হয়তো মাথা উচু করে যান বলছে☝☝ আর বাল বাংগালী কি বাল বোঝে,0,sports
রংপুর এর দর্শকরা কই গেলা হাত তুলো আর তাসকিন কে যারা জাতীয় দলে দেখতে চাও তারা লাইক কমেন্ট করো,0,sports
ঢাকা হারছে কস্ট পাইচি 😰😰😫😫,0,sports
সাকিব আল হাসান নিষিদ্ধ হয়েছে এখানে প্রতিবাদ করতেছে তোমরা আর আমার নবীকে খারাপ কথা বলে তার প্রতিবাদ তোমরা করো না,0,sports
রুবেল হোসেন = রিকশাওয়াল। <br />agree if then like the comment,0,sports
পাপন ভাইয়ের সাথে আমি একমত,0,sports
এটা পাপন মাদারির কাজ জেনে থাকলে বছর পর কেনো বলবে????,0,sports
কোটি টাকাএমন ভাবে বলতেছে মনে হয় তার পকেটের টাকা দিছেসালির ছেলে৷৷তারা অর্জন করে এনেছে টাকা সেই টাকায় তাদের দেয়া হয়ছেআর পাপনের এমন ভাব যেনে তার পরিবারের লোকজন প্লেয়ারসালা বলে যাদের পাবে তাদের নিয়ে ইন্ডিয়া সফরে যাবে মনে হয় ওর বাপের গাড়ের আইন ও জানে নাযে এটা ইন্টরনিশনালএটা শুধু ও চামচামি করেএখানে প্লেয়ারের ইচ্ছা সব হয়ভাই যারা লক্ষ টাকা বেতন শুনে অভাগ হচ্ছেনকেন ভাই অভাগ হনতারা তো আপনার আমার টাকা নেই নাতারা বিভিন্ন খেলাই যে টাকা টা টাই তা থেকেই তাদের বেতন টা নেইআমার আপনার টাকা দিয়ে যাদের সংসার চলেআমার আপনার টাকা না হলে যারা রঙ্গিন দালানে থাকতে পারবে নাতারা হল জারজ পুলিশআমাদের টাকায় চলে আমাদের উপরই গুলি বর্ষন করেআর প্লেয়ার তো দেশের কোচ আমর্পিয়ার কেই রিপেজেন্ট করতে চাচ্ছে এতে আমাদের দেশের জন্যই ভালোতাদের আমরা গালি দিতে অধিকার রাখি না প্রিয় ভাইয়েরা,0,sports
বন্ধু রা সাকিবাল হাসান ভাই আজমাঠে নাই তো তাই মাঠ টাই খালি খালি লাগ তে আছে,0,sports
"ছাত্রলীগ নেতা অধ্যক্ষকে কেমন মার মারল ভিডিও দেখুণ । CCTV cemera Videos Top News<br /><a href=""https://www.youtube.com/watch?v=H3YlX1uHVq0"">https://www.youtube.com/watch?v=H3YlX1uHVq0</a>",0,sports
যারা বাজে কমেন্টস করছো তাদের জন্য বলছি এক মাত্র তোদের কারণে বাংলাদেশ কোনো উন্নতি করতে পারে না,0,sports
পাপনের চালাকি,0,sports
বিশ্বসেরা ও বাংলার সর্বসেরা ক্রিকেটার সাকিব আল হাসান। এর চেয়ে বড় বিষয় হলো : পাপন পরিচিতি বাংলাদেশে বিশ্বে সাকিব পরিচিতি পাপনের মতো ঘাউরা বদমেজাজী এবং কথার ছলে বোকা বানানোর সুবুদ্ধি সম্পন্ন মানুষকে শিক্ষা দেওয়ার জন্য কাকে দরকার জানেন ? আমি জানি ভাবুন নামটা কিছুক্ষণ পরে লিখছি।,0,sports
বাংলাদেশের সব বাটপারের দল গালি দিয়েছে তাতে কি হয়েছে,0,sports
এখন ভাই তুমি খেলটা বাংলাদেশের হয়ে ছেড়ে দাও!বহুত খেলছোএই দেশে লিজেন্ড কীভাবে তৈরি হবে কেননা লিজেন্ডদের গুরুত্ব দেওয়া হয় না!বোকাচোদা বাঙালি,0,sports
বাংলাদেশের ক্রিকেট আর শেষ হয়ে গেলো।,0,sports
ভাইয়া সাকিব আমার প্রথম হিরো। সাকিব আমার কাছে ডিসি কিংবা মার্ভেল সুপার হিরো না। সাকিব আমার কাছে বাস্তব জীবনের হিরো। ছোট বেলা থেকে সাকিবকে নিয়ে হাজারো বার তর্ক করেছি৷ কারো কাছে হারতে দেইনি আমার সুপারহিরোকে। কিন্তু আমার সাকিবকে হারতে হয়েছে বিসিবির নোংরা রাজনীতির কারনে। হয়ত সাকিবের শাস্তি কমানো সম্ভব না। কিন্তু এই জারজ পাপন ও বিসিবিকে সরাতে হবে। পাপনের ক্যাসিনো খেলার ভিডিও বের হইছে। প্লিজ ভাই আপনারা এটা মিডিয়াতে ব্যাপক আকারে প্রচার করেন। এই পাপন ও সুজন বাংলাদেশের কোটি কোটি মানুষের স্বপ্ন কে গলা টিপে ধরেছে। ক্রিকেট নিয়ে আমাদের আবেগ ও অনুভূতিগুলোকে বাঁচান। প্লিজ,0,sports
তুই জানচ না,0,sports
অসাধারণ মেহেদী হাসান জাতীয় দলে এইরকম পারফরম্যান্স চাই,0,sports
মহা ভারত অশুদ্ধ হয়ে গেছে একেবারে। খারাপ খেললে তো সমালোচনা শোনা লাগবেই যদি সহ্য করতে না পারেন তবে বাড়িত যাইয়া ঘুমান খেলতে আইসেন না। পাবলিক সার্ভিসের ভালো মন্দ দুইটা দিক ই থাকে। খালি ভালা টাই গ্রহন করবেন খারাপ টা নিতে পারবেন না তাইলে খেলা বাদ দেন। আজাইরা যতসব ভালো একজন প্লেয়ার ভাবছিলাম বাট অহংকার আর আহমিকতায় ডুবে গেছে। একসময় বাংলাদেশে ফুটবল কিন্তু খুব বেশী জনপ্রিয় খেলা ছিলো এখন নাই ক্রিকেট ও যে তার জনপ্রিয়তা ধরে রাখতে পারবে তার ও কিন্তু নিশ্চয়তা নাই। সো দর্শক দের অবমাননা করবেন না। আপনি না খেললে আরো অনেক খেলোয়ার তৈরি হবে কিন্তু যদি দর্শক সেন্টিমেন্ট নষ্ট করে দেন তবে আর খেলাটাকেই আর টিকিয়ে রাখা সম্ভব হবে না,0,sports
"সাব্বির ঠিক করছে,",0,sports
তুই পাপন পদত্যক কর,0,sports
সালার বাচা লাথি মারবো,0,sports
এটা মটেও ঠিক হয়নাই পাতানো,0,sports
পাগলের বাচ্ছা বুয়া নিউজ খেমা কর,0,sports
ভাই কাল এক্সামসারাদিন পড়তেছিবিকেলেও ঘুরতে বের হয় নিকিন্তু আপনার ভিডিওর নোটিফিকেশন আসার সাথে সাথেই দেখা শুরু করে দিলাম,0,sports
ধন্যবাদ তাহসিন ভাই খুব সুন্দর ভাবে উপস্থাপন করেছেন 🙂☺,0,sports
পাপন হটাত ট্রিকেট।বাঁচাও,0,sports
রুবেল এর কারনে ম্যাচ টা হেরে গেসে তার বালের এক ওবার করছে,0,sports
সালা মিছা কথা কছ কে,0,sports
ভাই ক্রিকেট মাঠে কেমনে ১০০তে১০০??১১০ইনিংসে একটা ১০০নাই। গড সব ফরম্যাট মিলে ২৫ করে।খেলবে কি নারী নিয়ে ব্যস্ত।,0,sports
আমার মনে হয় ছেলেটা সত্য কথা বলতেছে।।কিন্তু মুসফিক একটু অন্য ভাবে নিছে।।যেহেতু আউট মন এমনিও খারাপ ছিলো,0,sports
ঠিকই ভাই বলছেন,0,sports
সাকিব একজন খেলয়ার আইন অবশ্যই জানেসে কেন জানায়নিসে নিজেও রাজিতুই কোন বালকয়টা কাপ আনছে নিজে কুটিকুটি টাকা বানাইছেদাবী নাই ধর্মঘট এটা পাগলের প্রলাপচোর চোরইবিসিবি কি করবে তুই একটা কর দেখি তুর হেডাম কত?,0,sports
রাজশাহীর এইবার একটা চ্যান্চ রাসেল এর খেলা ভালো লাগছে ফাইনাল জিতবে কে খুলনা রাজশাহী,0,sports
ভাই আপনার সব ভিডিও গুলা দেখিভাল লাগেসাকিব এর খেলাও ভাল লাগেকিন্তুআমার একটা প্রশ্ন সেটা হলোসাকিব কনভার্সেশন ডিলিট করে দিলো কেন? কি এমন কথা হয়েছিল তাদের মাঝেআর আগারওয়াল এর সাথে দেখা করতে চাইলো কেন?সাকিব এর কি নৈতিক স্খলন জাতীয় সমস্যা হয়নিযেখানে আরো অনেক সিনিয়র জুনিয়র প্লেয়ারদের ফিক্সিং এর অফার পেয়েছিলোতারা ঠিকি কে জানিয়েছিলআর একি বিষয় কয়বার ভুল হয়? তিনবার!,0,sports
মনে করছিলাম একটা জায়গা অাছে যেখানে কোন নুমরা রাজনীতি নাই।কিন্তু না।অামরাত জাতে বাঙ্গালী।এখানেও রাজনৈতিক বিষয় ডুকাতে হবে।বালের ক্রিকেট খেলা।,0,sports
অবসর সময়কি তোমরা এরকম কর,0,sports
ক্রিকেটের রাজপুত্র ❤💓💓💓💓💓অনেক বেশি ভালোবাসি,0,sports
মানুষের শুরু হয় ভালো দিয়ে আর DBC শুরু হয়েছে মানুষের বদনাম দিয়ে,0,sports
তোমাদের মতন কুলাঙ্গার সন্তানকে জন্ম দিয়ে মায়েরা সবচাইতে ভুল করছে তোদের মতন কুলাঙ্গার সন্তানকে জন্মের সাথে সাথে না গলা চেপে হত্যা করার প্রয়োজন ছিল,0,sports
"লম্বা সময়ের জন্য বহিস্কার করা উচিত বেয়াদবের,কারণ এদের কঠোর শাস্তি দিলেই সবাই সচেতন হবে।",0,sports
ভাই আপনাকে আর টিভিতে দেখিনা,0,sports
সেদিন পাপন বলেছেন মেচ পেস কিং খবর আসবে,0,sports
টাকার চাকরিজীবীর ছেলে টিকিট কায়টে এদের খেলা দেখতে যায় দেশকে সাপর্ট করার জন্য আর এরা টাকা বেতনে ও হয় না।,0,sports
ষড়যন্ত্রকারীর মুখে চক্রান্তের কথা।এই অপদার্থ কমিটিই মূল চক্রান্তকারী।সত্য প্রকাশ করে দেয়ায় খুব আতে ঘা লেগেছে!!!,0,sports
বাংলাদেশ ক্রিকেট খেলায় আগামীতে কাঙ্গালী হবে জিম্বাবুয়ের চেয়েও নগন্য হওয়ার পথে চলে যাচ্ছে।,0,sports
"পাগল ছাগল সাংবাদিক ,",0,sports
বাংলায় বলেন ।সমস্যা নেই ভাইয়া হয়ে যাবে।আমাদের মুসফিক ভাইও আগে এ কথা বলতে পারত না কিন্তু এখন বলতে পারে। হয়ে যাবে।,0,sports
সবাইকে সালের অগ্রিম শুভেচ্ছা। এবার কারা কাপ নিতে পারে??,0,sports
😂বিসিবির কাছে আমার অনুরোধসাকিবদের দাবি না মেনে ওদেরকে দল থেকে বাদ দিয়ে আমার মতো কিছু বেকারদের জাতীয় দলে সুযোগ দেয়া হউক।🤣🤣🤣বেতন যা দিবেন তাতে সন্তুষ্ট 😂😂 বেতন নিয়া আমার কোন দাবি নাই আর ভবিষ্যৎতে কোন দাবি থাকবো না।🤣🤣🤣 আমার দাবি কি মেনে নেয়া হপ্পে।🤣,0,sports
এটা বুঝাই যায় এটা পাপনের সাজানো নাটক বছর আগের ঘটনা এতদিন কারো কোন মাথা ব্যাথা ছিলো নাহ এখন কেন এসব নিয়ে মাথা চাড়া দিয়ে উঠছে? এগুলো পাপনের কারসাজি মানুষ এতো বোকা নাহ,0,sports
সৌস্য দা সেই সেই একটা ইনিংস উপহার দিলে ভাই অনেক অনেক শুভ কামনা তোমার জন্য💞❤️,0,sports
ফালতু কোথাকার।তুমি কোথা থেকে এই সংবাদ পেয়েছো??বেটা এতে করে সাকিবের ভাবমুর্তী নষ্ট হচ্ছে।,0,sports
আপনাদের কাছে চাইলেই যদি পাওয়া যায় তাহলে দাবি গুলো মেনে নিলেই তো হয়।সাপের মত এত রাগে ফোসছেন কেনো?,0,sports
পাপনের পদত্যাগ চাইঐ পাপন আপনি কিসের শক্😠😠😠,0,sports
মোপাসর তুমি মিতা কতা দরা পরে গেচ করান তুমি গুসের টাকা বাগ পাওনা তুমি জাননা বাংলার বাঘের বাচচা পাপন রাসটপতির জিললু রহমানের চেলে,0,sports
কে বলেছে এখন অন্যায়ের বিচার নাইতাদের জন্য এই দেখো বাস্তব প্রমাণ!!! মুরগি চুরির দায়ে গলায় ফাঁসি😭😭😭এই পাপন কে কিছুই বলার নেই?আমরা কি পারিনা তাকে গদি থেকে সরাতে?শেষ করে দিলো আশরাফুলের জীবন যার হাত ধরেক্রিকেট মাথা তুললো বিশ্ব বুকে।এখন শেষ করছে ক্রিকেটের মনি টাকেখুশিতো এখন সাকিব হেটার্সরা খুশি?আর একবছরের ভিতরে এই বেয়াদব কে দেখতে হবে নাকিন্তু আমিতো ভয়ে আছি সত্যি বড্ড ভয়ে আছিজানিনা অভিমানের জের ধরে আর কখনো যদিএই বেয়াদব টাকে লাল সবুজের জার্সিতে মাঠে না দেখি????জানি সবাই আমারা এক এক টা পোষ্ট দিয়ে দায় মুক্তহয়ে যাচ্ছিএক বার ভেবে দেখি আমরা এই বেয়াদব টারজন্যকি আমাদের কিছুই করার নেইআছে অবশ্যই আছে।এমন ক্রিকেট সে না খেল্লে তার কিছুই যাই আসে নাকিন্তু আমাদের অনেক কিছুই যাই আসেতাই আমাদের উচিৎ সকল ক্রিকেট খেলা দেখা থেকে বিরত থাকা।কারণ সারা বিশ্ব জানে বাংলার মানুষ কতোটা ক্রিকেট পাগলতাদের ছাড়া ক্রিকেট গ্লারি মোট ফাঁকা।আমার মতে সকল ক্রিকেটারের উচিৎ খেলা থেকে নিজেদের সরিয়ে রাখাপাপনের বিরুদ্ধে বিক্ষোভ করা।কারণ তাদের সাথে থাকবে আরো কোটি জনতা।,0,sports
সাকিব আল হাসান নিষেধাজ্ঞা না করে পাপন সাহেব নিষেধাজ্ঞা করার দরকার,0,sports
"রুবেল বাইয়া আপনি তো একটি মেয়ের জীবন নষ্ট কললেন আপনার বুকে আল্লাহ খোদার ঠাডা গজোব পরোক,।",0,sports
পাকিস্তান প্লাটুন,0,sports
বিলাইর বাচ্চার ভাব কত,0,sports
সাকিব বাই ছারা শক্তি তাকবে না কারণ সাকিব অনেক সাহসিনী,0,sports
পাপনের যড়যন্ত্র,0,sports
সাকিব কি কান্না করছে? চোখ লাল দেখা যাচ্ছে। 😭,0,sports
আমার বাসা খুলনা এবং আমিও খুলনার সাপোর্টার এবার কাপ ইনশাআল্লাহ আমরাই নেবো,0,sports
ওরে পাপন আর কত রাজনীতি করবি কর ক্রিকেট টাকে ধংস কর সব কিছু ত শেষ তদের ত দিন,0,sports
বোকার মতো কমেন্ট করবেন না।।। ওইখানে দশকের দোশ ছিলো।।।। খেলোয়াড় দের দোস নাই।।। দশক সাধারণ মানুষ তাই তা দোস কেউ দেখতে পায় না।।।।মুসফিক স্টার তাই তার দোস সবাই দেখে।।। এইদেশে প্রতিভার ক নো মুল্য নাই,0,sports
তরা হচ্ছিস অশিক্ষিত ব্যাটম্যান তরা রান করার পর কি করতে হবে সেটা মাথাই আসে না তরা রান কে পঞ্চশ পাবে না ও রান কে করতে পরবে না যেটা পারবে শুধু ক্যাচ আউট হতে। তদের মাথাই শুধু একটা জিনিসয়ে গুরে সেটা হল ছক্কা মারতে গিয়ে ক্যাচ আউট হওয়া ও যত বেশি ডট বল খেতে পারিছ। না হয় এত বছর জাতিয় দলে খেলে স্মার্ট ব্যাটসম্যান হতে পারলেই না। সমস্য নেই প্রতি মাসে তো বেতন পাচ্ছি জাতিয় দলে চুক্তি তো আছিয়েই।। তোমরা যেটা পার না সিঙ্গেল রান বেশি নিতে টু রান বেশি নিতে প্রতি ওভারে একটি চার মারতে শুধু পারিছ ছক্কা মারতে গিয়ে আউট হতে।। বলছি বিশেষ করে সৌম্য সাব্বির লিটনদে উদ্যশে,0,sports
সাব্বিরের উজ্জাবন ঠিকই আছে কারণ তার প্রথম সেঞ্জুরি এটা তাই তার উত্তেজনা একটু বেশি থাকবেই।,0,sports
আরে বেটা পাপর ওরাতো শুধু জাতিয় দলের জন্য দাবি গুলো করে নাই। দাবি গুলো ক্রিকেটের সর্ব স্তরের জন্য।,0,sports
হাইলাইটস এর একটা লিমিট থাকে আশা করি সেটা খেয়াল করবেন। মিনিটের হাইলাইটস মিনিটে কি হয় কিছুই বুঝলাম না।,0,sports
ভিডিও দেখে যা বুঝলাম।। এখানে গালিটালি কিচ্ছু না মুশফিক আউট হইছে এমনিই মাথা গরম তারপর এই দর্শক উপরের দিকে তাকান এই কথাটা তার বুকে তীরের মত লাগছে তাই একটু ক্ষেপেছিল হয়তো।। আর এদিক দিয়ে কিছু চামচা এসে জল ঘোলা করতেছে,0,sports
ভারতের সাথে খেলার পর ধর্মঘট করতে পারতো। এদের খেলার প্রতি মনোযোগ নাইসবার সাথে গু হারা হারে। আর এদের খালি টাকার ঠাণ্ডা। সাকিব এর আর কতো টাকা চাই?,0,sports
ফকিন্নির বাচ্ছা,0,sports
কিছু বলার নাই ভাইশুধু 😭😭😭😭😭😭😭😭😭😭😭😭😭😭😭,0,sports
"ম্যাচ হারলেও সমস্যা, জিতলেও সমস্যা, সেলিব্রেশনেও সমস্যা, তাহলে ক্রিকেটারটা করবে টা কি?আজব জাতি বাঙ্গালী।",0,sports
প্রিয় বোলার যখন ছন্দে থাকে তখন আমার অনুভূতি টাই অন্যরকম এগিয়ে যাও বস ভালোবাসি,0,sports
আপনার কাছে ওহি আসছিল?,0,sports
বিসিবি চরম বোকামি করলো।,0,sports
এমনও হতে পারে তার উপর কোন গুরুতর হুমকি ছিলো। হতে পারে ফ্যামিলি বা নিজের উপর। এজন্যই হয়তো ইগনোর করে গেছে।,0,sports
ম্যান অফ দ্যা সিরিজ রাসেলকে দেওয়া উচিত হয় নি,0,sports
ভাই আপনি লাস্ট যে প্রশ্নটা করছেন এটা করা লাগে নাকি আবার বাংলাদেশের ছোট ছোট বাচ্চার বলবে সাকিব দলে না থাকলে বাংলাদেশ দলের কি পরিনতি হবে সেটা আল্লাহই জানে আমরা খালি এটাই বলতে পারি সাকিব ভাইকে দলে সাই,0,sports
পাপন স্যার খুব ভাল কথা বলছেন টেস্ট ম্যাচ খেলতে ভুলে গেছেন খেলোয়াড় রা এদেরকে আরও একটা করে বিয়ে করিয়ে দেওয়া উচিত আমি মনে করি ।,0,sports
যত কিছু ই বলছ তোর লজ্জা নাই আর এবার পদত্যাগ ছাড়া ও উপায় নাই,0,sports
নাসির আমার বাল খেলে,0,sports
আমার মনে হয় ছেলেটা বলছে আর মুশফিক মনে হয় শুনছে এটাই হবে সমভ্যাবতো। আর সালার চামচা গুলারে ঝাটা দিয়ে পিটানো দরকার যতো সব ফালতু গাজাখোর লোক গুলা😡😡😡😡,0,sports
পাপন সাহেবকে সভাপতির পদ থেকে যতদ্রুত সমভব বাহির করতে হবে,0,sports
মহানবি হযরত মুহাম্মদ সাঃ এর ভক্ত আছো কে কে সাড়া দাও আর আমার চেনেল সাব্স্ক্রাইব করতে কেউ ভুলো না,0,sports
বাঞ্চুদ রা কি উপরে গাজা খেয়ে লেখছে সিলেট বনাম রাজশাহী 😡😡😡😡,0,sports
কিছু বলার নাই অমিত ভাই।কথা গুলো একদম দিলে লাগে।😰,0,sports
এরকম খেলল্লে খুলনাই কাপ নিবে,0,sports
সাকিবের শাস্তিতো দূরের কথা তার সাথে যে অন্যায় হলো তার জন্য তাকে ক্ষতিপূরণ দেওয়া উচিত।,0,sports
তুমি বেয়াদব আমি মানি তবে তোমাকে ভালো না বেসে পারি না তোমার এই দুর্দিনে তোমার পাশে আছি আমরা তবে এখানে একটা ষড়যন্ত্রের আভাস পাচ্ছি আমি আমার মনে হয় পাপনের মত বেয়াদব কে আমাদের বিসিবি থেকে অব্যাহতি দেওয়াটা উচিত,0,sports
ভূয়া সংবাদিক,0,sports
কুমিল্লাতে কয়টা দেশি ছাগলেরা বাল ফালাইতে খেলে।,0,sports
তোমার কোন দোষ নাই।।সাকিব ভাইকে খেলাতে দেখতে চাই।,0,sports
"সেজদা টা কেউ দেখলো না ,হাত নারাটা দেখছে বালা",0,sports
একটা যে কোন দেশের ক্রিকেট দলের সভাপতি হওয়া উচিত সেই দেশের মান সম্পন্ন কোন খেলোয়ার যে ক্রিকেট বুঝে এবং ক্রিকেট জানেকোন রাজনৈতিক পরিবারের বিতর্কীত ছেলের ক্রিকেট সভাপতি হওয়ার যোগ্যতা রাখে না যেমন নাজমুল হাসান পাপন,0,sports
যেই বাল খেলে আবার টেকা চায়,0,sports
এই রকম খেলা ভালো না এটাতো ফাজলামো কানের মধ্যে লাগলে কানের পর্দা ফেটে যায় যতসব পাগল ছাগল,0,sports
বিপিএল এর ড্রোন নাকি হারায় গেছে।😃,0,sports
পাপন হঠাও ক্রিকেট বাচাও,0,sports
এই বেটা স্কয়ার নাম কিছুইতো দেখা যায় না কি দেখাচ।,0,sports
ভাই খেলোয়ার হলেও তো মুসফিক ভাই মানুষ।সে ভুল করতেই পারে।একজন ভক্ত হিসেবে তারও তো কিছু বলা কিছু সাজেশন্স থাকতেই পারে।মুসফিক ভাই ও তো একদিনে আজকের এই মুসফিক হয় নাই।আমাদের মত সাধারন মানুষের ভালবাসায়ই তো আমাদের ভাই মুসফিক।বাট ভিডিওটা দেখে মনে হলো লাস্টে আড়ালে নিয়ে হয়তো কিল ঘুসি এটা তো বাড়াবাড়ি। যেটা দেশের ক্রিকেটের ভাবমূর্তি কি বাড়াবে,0,sports
মজা নাই জনশূন্য এভারের বিপিএল,0,sports
নাইম ভাইয়াকে জানাই আন্তরিক অভিনন্দন ভালো খেলার জন্য,0,sports
মুশফিকুর রহমান কে,0,sports
আপনি চলে যান।কারন আপনি বিনা ভোটের চেয়ারম্যান।,0,sports
হিংসার রাজনীতির স্বীকার সাকিব পাশাপাশি সাকিবেরও ভুল। ভারত সিরিজ নিয়ে এতো ঝামেলা এই দেশটার কারনে এতোকিছু,0,sports
পাপন কিছুই জানে না তুই কিসের সভাপতি। সারা দিন ক্যাসিনো আর মদ খাইলে জানবি কেমনে,0,sports
সাকিব যদি ইংলান্দের হয়ে খেলে তাহলে ভাল হবে কারন দেশে সুধু দুরনিতি,0,sports
ইতর সরাও ক্রিকেট বাচাও !,0,sports
প্রথম সেঞ্চুরি তো ভাই তাই হয়ত এমন করছে...,0,sports
পাপন ভাইয়ের কথায় যুক্তি আছেসুন্দর ভাবেই যুক্তিগুলো তুলে ধরেছেআমরাও দেখতে চাই কারা বাংলাদেশ ক্রীকেট টা কে নিয়ে ষড়যন্ত্র করতেছে!!,0,sports
বল করল গতি দানব এই সালা আবার বলিং সিকল কবে।তাও আবার লাস্ট অভার।হাহাহা,0,sports
এটা কোন ধরণের সুপার ওভার? মাএ রান 😡😡,0,sports
বাংলাদেশীরা কাকড়ার জাত।,0,sports
পৃথিবীতে সবাই আপন হয় নাকেউ কেউ পাপন ও হয়।,0,sports
ভালোবাসার এক নাম,0,sports
আন্দোলন তো হবেই সাকিব কে নিয়েই,0,sports
সালার বাংলাদেশ রাসেল গেইল এদের মতো বা কোহলি রোহিত এর মতো কোনো ম্যান পেলাম না কপাল কুথথা বাগগ,0,sports
তাসকীনের দাঁত ভাঙা কেনো? তাসকীনকে গে দের মত লাগে,0,sports
হাবিবুল বাশারকে বিসিবির প্রধান চাই ওয়েলকাম হাবিবুর বাশার স্যালুট জানাই আপনি আসলে সেব চেন্চ হবেখেলা টা খেলার মুত হবে,0,sports
তোর মতো ছোর দূর্নিতিবাজকে আমরা আর দেখতে চাইনা।,0,sports
সালে এসে মাশরাফি বসের শেষের স্ট্রিমরোলার দেখলাম♥,0,sports
কিরে বেজন্মার বাচ্ছা না জেনে ফালতু নিউজ করলি ক্যান ? তোদের মত কিছু ইউটিবারের জন্মের ঠিক নাই । এই জন্যই তোরা সস্তা জনপ্রিয়তার জন্য ভুল বাল তথ্য দিস । সাকিবের জন্য এমনিতেই মন খারাপ হয়ে আছে । সঠিক তথ্য দিস । সামনে ফাইলে তোর মাথা নামিয়ে দিব শুয়রের বাচ্ছা ।,0,sports
পাপন কে নির্বাচক থেকে বাদ দেওয়া হোক,0,sports
টি ভাই ধন্যবাদ আপনাকে ভাই,0,sports
বালের বালের চেলেন চালাও কিছু না বূইজাই ছারছো,0,sports
ক্রিকেটের মাইরে চু। আর দেখবো না।,0,sports
পাপন সাহেবের স্বার্থে আঘাত লাগছে।,0,sports
আমরা ছিলাম আছি এবং থাকব আপনার অপেক্ষায় কোব ভালো থাকবেন আমাদের দোয়া সব সময় আপনার সাথে থাকবে(পরিবারকে সময় দেন💐💐💐),0,sports
ভাই কথা একটাই আমাদের ক্রিকেটে রাজনীতি ঢুকে পড়ছে <br />ওই পোকা যতদিন দমন না হবে ততদিন তর্ক বিতর্ক থাকবেই!!,0,sports
সাব্বির&quot; তারকা হইলো কেমনে..???,0,sports
আসসালামু আলাইকুম ভাইয়া।। আমরা অকৃতজ্ঞ তাই তাই আমাদের দেশের গর্ব আর অহংকারের গায়ে আমরা কাদা ছুটছি।।।আমরা বোধহয় বাংলাদেশের অস্তিত্ব মুছে ফেলতে চাচ্ছি😭😭😭😭😭।।প্রথমে আশরাফুল এখন শাকিব৷আমাদের লজ্জা হওয়া উচিত।।।,0,sports
সাকিব ছাড়া বাংলাদেশ দল মুল্যহিন,0,sports
মিরাজ ভাই এইটা ধরে রেখ ভাই,0,sports
আপনারা যে চোর সেটা জনগণ ভালো করে জানে আর জনগণের সামনে দুধে ধোয়া তুলসীপাতা হওয়ার প্রয়োজন নাই,0,sports
আমাদের দেশের খেলোয়াড়দের চর্বি বারছে।।বন্ধ করে দেন সব কিছু কি বাল হবে দেশের।। খোলা বন্ধ করে দিলে কই পাবে এতো দাবি।।।না খেললে বাল হবে দেশের।কেনো জাপান আমেরিকা খেলে না যে কি হয়।।।যতসব দেশের মোখে কালি।।।সব আবাল,0,sports
আন্তর্জাতিক ম্যাচে খেলতে পারবে,0,sports
পাপন কে থেকে বহিষ্কার করা হোক ।,0,sports
সবডিরে জুতা দিয়া বাইরানের দরকার।,0,sports
একে এ পেজেনটেশন করতে দেয় কে।ওর তো দলের নামই মনে থাকেনা। ও রাজস্থান রয়েলস কোথায় পেলো।,0,sports
পাপন সাহেব আগে নিজের চরকায় তৈল দেন মিয়াআপনি বাবা মার মান ইজ্জত ডুবিয়েছেন,0,sports
স্যার আপনে পদত্যাগ করেন।। কারন অনেক দিনতো হল।নতুন ভাবে সব নিয়োগ করেন।।।পুরো বোর্ড।।আপনাকে সম্মান দিয়ে বললাম,0,sports
"তোর চাইতে হির আলম কে আরো বেশি সুন্দর লাগে, আর তোকে নিয়ে না কি মেয়েরা স্বপ্ন দেখে,এটা হাইস্য কর,হেপি আপু যে তোকে ভালোবাসছে এটা তোর কপালের ভাগ্য,কোথাই হেপি আপু আর কোথাই তুই, কোথাই আগর তলা আর কোথাই চকির তলা,",0,sports
পাপনের পদত্যাগ করা উচিৎ,0,sports
সে একা না সাব্বির রুবেল ও নাছির সবাই কে নারী কেলেঙ্কারির দায়ে ফাঁসি দেওয়া হোক,0,sports
সাকিব ভাইকে মাঠে দেখতে চাই। আর পাপন বন্ধুকে মাসের জন্য নিষিদ্ধ দেখতে চাই,0,sports
পাপনের পরিবর্তে এই জায়গাটিতে মাশ্রাফিকে দেয়া হোক শবাই একমত হলে লাইক দিয়ে সমর্থন করুন,0,sports
ভাই সালা পাপনের কাজ সালা পাপন কিকেট সেস করেদিবে,0,sports
মিনিমাম প্রতি ম্যাচে টা ব্যাটসম্যানের সেঞ্চুরি ও দুইটা ব্যাটসম্যানের হাল্ফ সেঞ্চুরি চাই। যেকোনো একটা বোলারের টা উইকেট চাই।ক্যাচমিসফিল্ডিং মিস করলে তারোকা হোটেলের পরিবর্তে মাঠেই রাত কাটাতে হবে অথবা পাছায় টা বেতের বাড়ি।👇👇👇👇👇👇👇👇👇,0,sports
আমি রুবেলের বরো ফ্যান,0,sports
নাজমুল হোসেন পাপনেরপদত্যাগ চাই।,0,sports
আকরাম খান সুজন নান্নু এদের বাদ দিলে সাকিব বাহিনী ভালো খেলবে ইন শাআল্লাহ,0,sports
হয়তো কোন রাজনীতি থাকতে ও পারে যেহেতু শাকিব দোষ স্বীকার করেছেন নিয়ম অনুসারে শাস্তি হওয়া উচিত,0,sports
পাপন কে জুতার মালা পরিয়ে দেওয়া হোক,0,sports
সাকিব জদি কোন দিন নাও খেলে। সাকিবের একটা বাল ও পরবে না,0,sports
আইসিসি যখন গোস কাই তখন কারো কিছু বলার থাকে না,0,sports
সাকিব যেদিন মাঠে ফিরবে সেদিন থেকে খেলা দেখব,0,sports
বাদ বাদ,0,sports
আনি আবারও বলবো সুজন পাপন আকরাম মোট কথা তোমরা আগে বাদ হও তা হলে ঠিক হয়ে যাবে সব । আর একটা কথা আমিতো বেস কয়েক বছর আগে চ্যালেঞ্জ করে বলেছিলাম আমাকে কোচের দায়ীত্ব দেওয়া হউক ক্রিকেট আর বিপর্জয়ে পড়বেনা ।,0,sports
আগারওয়াল এর নিউজ কই।সব বাটপার।,0,sports
খেলোয়াড়দের গালাগালি করে!!! ব্যবহার শিখে নাই।,0,sports
ঘুম থেকে উঠেই সাকিব আল হাসান মাসের জন্য নিষিদ্ধ হতে যাচ্ছে এমন নিউজ দেখার জন্য মোটেও প্রস্তুত ছিলাম না 😥সাকিবের অপরাধ তার সাথে বছর আগে জুয়ারিরা যোগাযোগ করে ছিল।সে তখন তা প্রত্যাখান করলেও আইসিসি কে কেন জানায় নি।ওরে পাপইন্নার বাচ্চা আমরা ফিডার খাই না আমরা বুঝি তোদের বিরুদ্ধে আন্দোলনে নেতৃত্ব দেয়াটাই কাল হয়ে দাড়িয়েছে সাকিব ভাই এর জন্য।নতুবা বছর আগে কার সাথে ফোনে কথা হয়েছিল সেটা আইসিসি তখন না জেনে এখন জানবে কি করে😡এখনও সিউর না শাস্তির ব্যাপারে যতক্ষন না আইসিসি ঘোষনা দিচ্ছে তবে যদি সত্য হয় তাহলে সাকিবের নয় ক্ষতি টা হবে বাংলাদেশ ক্রিকেটের ই বেশি।কারণ পাপন রা প্রতিদিন জন্মালেও সাকিব রা যে হাজার বছরে একবারও জন্মায় কিনা সন্দেহ😒পাপন সুজন হটাও✊ বাংলার ক্রিকেট বাঁচাও💘🙏 😭,0,sports
তুমি না থাকলে আমরা খেলা দেখবোনাফিরে এসো তুমি,0,sports
ক্রিকেট প্রেমিসাকিব নাই মানে ক্রিকেট নেই।বালের ক্রিকেট কে বিদায় জানালাম🙏🙏আজ থেকে না দেখবো ম্যাচ না দেখবো ক্রিকেট নিউজ।কি দেখবো খেলা দেখে মাঠে কি পাপন নামবে কে এনে দিবে জিত।কান্না চলে আসছে😓😓😓😓😓😓😓😓,0,sports
আমি বুঝলাম না মাহমুদুল্লাহ এর ছয় কেন তিন বার দেখালো 🤔🤔🤔,0,sports
আমার চেনেলি গিয়ে ঘুরে আসুন।,0,sports
ওরে জুতা দিয়ে পিটিয়ে তারপর বের করে দেওয়া উচিত ওর চেয়েও অনেক বেশি ভালো খেওয়ার খুলনার ভেতর আছে,0,sports
আফ্রিদি কোথায়,0,sports
অাহা পাপন 😂,0,sports
শুনে খুব মজা পাইলাম।,0,sports
ভাইয়া আমিও অনেক সময় কাদছি😭😭😭। ভাইয়া কে যে অনেক ভালোবাসি💖💖💖।,0,sports
সেই থেকে চট্টগ্রাম আমার প্রিয় টিম ইনশা আল্লাহ এবার এরাই ট্রফি নিবে😍,0,sports
ইমরুল কায়েস এরকম মারলেন কিভাবে বুঝলাম না 😱😱,0,sports
আমি সিলেটি তাই বলছি আমাদের সিলেট জিতবে মনে হয় না বাজে টিম করেছে।।। সব সময় বাজে।।,0,sports
এসব কিছু নাএটা একটা চক্রান্ত যার সাথে বিসিবি সরাসরি জড়িতপাপন কাক্কু দীর্ঘজীবী হোক,0,sports
ভাইয়াইচ্ছা করে আপনার মতো মন খুলে কথা বলিজানেনই তো ব্যক্তিগত মত প্রকাশ করা মানেই দুনিয়া থেকে ব্যান হয়ে যাওয়া।,0,sports
বালের মুসফিক দিয়ে দেশের কি লাভ আমার সালা রা,0,sports
পাপকে সবাই লাথি মার ও এখন ও কেন জিবিত?,0,sports
একশত পারসেন সত্য খতি হবে বাংলাদেশের,0,sports
পাপন নান্নুকে বাদ দিলে সবাই শান্তি পাবে,0,sports
কাদের জন্য আজকের এই মুশফিক উনি অপরাধ করে থাকলেও উনার সাথে যা করা হলো তাতে কি মুশফিক অনেক শান্তি পাবে,0,sports
বিশাল বড় খতি হবে,0,sports
বর্তমানের মিডিয়ার কাজই হলো তিলকে তাল বানিয়ে প্রকাশ করা,0,sports
একটা দেশের বোর্ড সভাপতি মিডিয়ার সামনে এসে বলছে ওমুকের বাবাকে আমি বাচিয়েছিতমুকের খালাকে আমি বাঁচিয়েছিতমুক রে জেলে নিয়ে যাওয়া হচ্ছিল আমি ছাড়িয়েছিতমুকের বাচ্চাকে নিয়ে বিদেশ যাবে আমি ব্যাবস্থা করে দিয়েছি। উপরিউক্ত কথাগুলো বলেছে দফা দাবীর পরিপ্রেক্ষিতে। ক্রিকেটীয় দাবীর জায়গায় অন্য কোন্দলদেশ ষড়যন্ত্রপ্লেয়ারদের থ্রেট এইসব লেইম কথাগুলো শুনেই বুঝা যায় যে উনি কি শক্তিমত্তা দিয়ে বোর্ডে টিকে আছেনক্লিয়ারলি বুঝা যায় যে উনি রাজনৈতিক শক্তিমত্তা দিয়ে বোর্ডে এখনো টিকে রয়েছেন।উনার কথাবার্তা শুনে মনে হয়েছে যে উনি প্লেয়ারদের দফা দাবীর ব্যাপারে কম প্লেয়ারদের থ্রেট দেওয়ার জন্যে মিডিয়ার সামনে এসেছে। একজন বোর্ড সভাপতির কথাবার্তা এমন কিভাবে হয় কখনো ভেবেছেন? অবশ্যই তার সেই উপর থেকে কোনো পাওয়ার আছে তাই তিনি মিডিয়ার সামনে এসেছেন এবং বলে গেছেন।অন্যান্য বোর্ডের বিরুদ্ধে সব খেলোয়াড়েরা একত্র হয়ে এভাবে আন্দোলন করলে বোর্ডের টনক নড়ে যেতো। দাবী মানতে না পারলে বোর্ডের কর্মকর্তা এবং কর্মচারীরা বোর্ড থেকে লজ্জায় সরে দাড়াতো কিন্ত না পাপন এসে সুন্দর করে বলে আরেক কথা ;খেলোয়াড়রা খেললে খেলবে না খেললে নাই; বাহ এ যেন কেউ বলতেছে যে ভাত খায়লে খাবি নাহলে নাই পেটে খুদা লাগলে তো দৌড়ে আমার কাছেই আসবি খেতে।যে দেশে দীর্ঘ বছর যাবত এক তামিমমুশফিকসাকিবমাহমুদউল্লাহমাশরাফির ধারেকাছেও কোনো বিকল্প বের করতে পারেনি সেই বোর্ড আবার গোটা ক্রিকেট জাতকে বলে উঠে খেলোয়াড়রা খেললে খেললে খেলবে না খেললে নাই। ইশ কথাবার্তা এবং থ্রেট শুনে মনে হচ্ছে উনি একাই ক্রিকেট খেলবেনএকাই বোর্ড চালাবেন একাই সবকিছু করবেন।এতেই বুঝা যায় উনি কিসের ভিত্তিতে এখনো বোর্ডে টিকে আছেন।কিসের ভিত্তিতে টিকে আছে সেটা ;বুঝলে বুঝন্তি আর না বুঝলে দৌড়ন্তি;। 😉এভাবে চলতে থাকলে জিম্বাবুয়েকেনিয়া হতে বেশি দেরি নেই এ দেশের ক্রিকেট। আমাদের ক্রিকেট আমাদেরকেই বাচাতে হবে।বয়কট পাপনবয়কট বিসিবি,0,sports
এদের গাজা দেয় কে,0,sports
এটাও গুজব।,0,sports
রাজশাহীই সেরা,0,sports
মজা পাইছি ভাই😀😀😀😀 কিন্তু তাসকিন ভাই এসব খেলার কোন দরকার ছিল না দ্বিতীয়ত ভোটের ফলাফল হিসেবে এটা কি ঠিক করল ছেলেটা অনেক ব্যথা পাইছে 😭,0,sports
এইরকম কাউন্টার খেলা আর কখনো হইনি বিপিএলে,0,sports
দুই পাগল,0,sports
তামিম প্রায় সব ম্যাচ এই একা টানছে দলকে।,0,sports
পাপন্নার কারণে দলটা দংশ হবে এই হালারে জুতা মারা দরকার🙄,0,sports
তোর মার হেডা,0,sports
টিক বলেছেন ভাইয়া i Love sabbir,0,sports
সাকিবকে ছাড়া বাংলাদেশের খেলা কিভাবে দেখব?,0,sports
হা হা হা হা আমার ভাই...,0,sports
ধন্যবাদ ভাই এত সুন্দর করে ভিডিওটি উপস্থাপন করার জন্য 😍😍😍 ❤ ❤যারা যারা বাংলা ড্রামা দেখতে খুবই পছন্দ করেন তারা আমার চ্যানেলটা এসে ঘুরে যেতে পারেন আমি প্রত্যেক বাংলা ড্রামা আমার চ্যানেলে আপলোড দিয়ে থাকি 🎥🎬📽,0,sports
ম্যাচ ফিক্সিং।।।,0,sports
পাপন সাহেব আমরা আপনাকে আর দেকতে চাইনা শরে দারান আপনি,0,sports
এখন ক্রিকেট পাপন দা খেলবে,0,sports
মুসফিকের সাফোটার টা বড় বেয়াডব,0,sports
ছিঃ ছিঃ ছিঃ...আমাদের বাংলাদেশের জাতীয় দলের সব খেলোয়ারের ভাষা কী এমন!!!!,0,sports
ওর বাবা জিল্লুর রাহমানতো খুব ভালো ছিল। কিন্তু ওই পাপন ওই রকম কেমনে ওইল। ! ! !আর একটা কথা আবরার এখন শেষ সবাই ভুলে গেছে।! ! !,0,sports
এতো সর্ট করলে হয় না।। মিনিমাম মিনিট করা উচিৎ,0,sports
আমি পাপনের পদোতেগ চই,0,sports
জুতা পিটা করা উচিত।,0,sports
এত লুইচ্চা কেন আমাদের ক্রিকেটার রা?,0,sports
ওহাব রিয়াজ গাঁজা ভর্তা খেয়ে নামছিল🌿,0,sports
আমি চাই সাকিব ইংলেন্ডের হয়েখেলুক তাতে বালো হবে বাংলাদেশ টিমে পাপন খেলুক হেডাম কত টুক,0,sports
অবশ্যই বড় ধরনের একটা ক্ষতি হবে,0,sports
হুগা কও মিয়া,0,sports
আমি খুব হতাশ হয়ে গিয়েছি,0,sports
পাপন কাক্কু যেমনই হোক কথা গুলায় কিন্তু লজিক আছে।।,0,sports
ইয়েস ক্ষতি হবে,0,sports
মুশফিকের এত রাগ আগে জানতাম না আর ছেলেটা যায় বলুক বাইরে কান দেবেন কেন খেলায় মনযোগ দেন আপনি হয়তো জানেন না এই ঘটনায় আপনার অনেক সাপোর্টার কমে গেছে,0,sports
ভাই এসবি আন্দোলন কেন করলো তারিই প্রতিফলএক কথায় বাংলাদেশে কেউ যদি ফেমাস হয় তাদের অবস্থা এমনিআমার তো মনে হয় ক্রিকেট বোডে যারা দায়িত্বে আছেন তারাই বর্হিবিশ্বের কাছে বিক্রি হয়ে গিয়েছে,0,sports
জর্জিয়ায় ভ্রমণ শিক্ষা বিনিয়োগ এবং রেসিডেন্স পারমিট এর জন্য যোগাযোগ করুন শাফি,0,sports
আমি বুজলাম না যেটা গটেছে তার পড়ে ও কেন তাকে হ্যারেজ ম্যান করা হলো সত্যি পোশাক পড়া লোকরা তো দেখছি নিশা খোর প্লিজ দয়া করে কেও আপনেরা দর্শক দের কে হয়রানি করবেন না প্লিজ,0,sports
কি কম্পিটিশন রে ভাই!!!! হিহিহিহিহিহিহিহি গ্রেট থাপ্পড়ানী,0,sports
নাজমুল হাসান পাপন কে জুতাপেটা করে ভোট থেকে নিষিদ্ধ করা হোক। সাকিব ভাইকে কেন বিনা অপরাধে অপরাধী বানাল। এটার কারন একটাই খেলয়ারদের বেতন বারানোর আবেদন করছে বলে। তাই সেই রাগটা সাকিব ভাইয়ের উপর মজাইছে। তাই বলছি ওর মতো বিসিবিকে বরিষ্কার করা হোক।,0,sports
আপনি যদি সব জানেন তাহলে সবার সামনে প্রমান করে দিন ?🆗,0,sports
পাপনকে বুয়েছ কোর করা হক,0,sports
মুশফিকুর রহিম কে টুর্নামেন্ট এর সেরা ঘোষণা করার দরকার ছিল।,0,sports
বাংলাদেশের পাব্লিক সব কিছু তে বেশি বেশি 😐,0,sports
হায়রে বাংগালি নিজের নবিকে গালি দিলে বিচার নাই,0,sports
পাপন শালাকে শবাই ধরে মার।,0,sports
রাজশাহীর সাপোর্টার কারা অাছো তারা সারা দাও।,0,sports
কালকে এটা ভাইরাল হয়ে যাবে,0,sports
ভূঁইয়া খবর,0,sports
খেয়াল করে দেখেন তো ;ছাগল একটা; এই কথাটা শুনতে পান কিনা এ,0,sports
সাবেক রাষ্টপতির ছেলে পাপন তার মা বাংলাদেশ আওয়ামীলীগ এর এক জন সাবেক নেএি কিন্তু শালা পাপন বাবা মায়ের অর্জন নষ্ট করল।,0,sports
বাল কাছ করেইনাই,0,sports
ওনি নিজেও একজন সরজনতকারী কমতা টিকিয়ে রাখতে হলে হাজারো সাকিবের কোরবানি দিতে পিছ পা হবে না আপনাদের মাননীয় প্রধানমন্ত্রী,0,sports
ভাই আগামী দুই বছরের ভিতর বাংলাদেশে কোন টিম কে হারাতে পারবে না শুধু হারবে বাংলাদেশ এখন,0,sports
ব্যাট কথা বলেছে। ও ওর মত খেলুক।,0,sports
আসুন আমরা নিয়মিত 5 ওয়াক্ত নামাজ আদায় করি ? আল্লাহ এই রমজান মাসে আমাদের সবাইকে কবুল করুন আমীন,0,sports
একমাত্র পাপন সাহেবের জন্য ক্রিকেট ধ্বংস হতে যাচ্ছে,0,sports
ভারতে একজন বিসিবি সভাপতি নির্বাচিত হয়েছেন তাদের ক্রিকেট খেলোয়ার দের মধ্য থেকেআর আমাদের দেশে বোকচো,0,sports
সব চাইতে ভালো হয় বিসিবি বসসস কে তিন ফরমেটের ক্যাপ্টেন সহ কোচ করা হউক😒 ফুটবল টা এই করেই শেষ হয়েছিল এখন ক্রিকেট টা সেই পথে আছে।,0,sports
সে অনেক ভালো,0,sports
গবেট ক্যাপশন বাজ 🥴,0,sports
বদমাইশ তোরা কি নিউজ করো শালা,0,sports
ভাইয়া পাপনের ক্যাসিনো ভিডিও পাস হয়েছেএইটা রিপোর্ট করেন,0,sports
সবাই পাপনের সয়তানী,0,sports
ধন্যবাদ ভাইয়া ভিড়িও টি বানানোর জন্য,0,sports
ডাল ভাত শট😂😂😂ওহ শামিন ভাই আপনার কমেন্ট্রি কিন্ত সেই লেভেলের জোশ 😁,0,sports
লোকটা গালি দিলে ভালই করছে আমি মনে করি লোকটা মুশফিক কে অনেক ভালবাসে মুশির বাজে পারফরম্যান্স সহ্য করতে পারে নাই। আপনারা বলুন তো বাংলাদেশ টিম এর কেও ফরমে আছে নাইতো। আমাদের টিম এর কোনো উন্নতি নেই আর নাই বলেই আফগানিস্তান বাংলা বাশ দেই গ্যালারি তে অনেকেই বাজে কমেন্ট করবে তার জন্যই খেপে যাওয়া মুশি ভালো করে নাই ইন্ডিয়াতে দেখেন ক্রিকেটরা যখন ভালো খেলেনা দর্শক রা জুতা পর্যন্ত মিলে,0,sports
সাকিব যে দিন থেকে খেলা শুরু করব সেদিন আবার খেলা দেখবো৷ 💔💔 💞💞💞,0,sports
লজ্জা তাসকিন লজ্জা,0,sports
চাচা ঠিক রাস্তা অাছেন,0,sports
পাপন মুক্ত করা হোক,0,sports
বস তোমাকে হাজার সালাম !!!,0,sports
রাজশাহী কে সুন্দর একটি উপহার দিলো আফিফ ভাই আশা করি রাজশাহী ভিবাগের মানুষ কখনো ভুলবেনা,0,sports
আপু আপনি তো জাতীয় কথাটাই উচ্চারণ করতে পারেন না দেখি,0,sports
এখানে অনেকে দেখছি দিয়েছে আমি জাতির কাছে প্রশ্ন করছি এরা কারা?,0,sports
কে বহিস্কার করা উচিত,0,sports
খুলনা বাদ যাওয়ার সম্ভবনা বেশি শেষ মেষে কুমিল্লা উঠে যাবে আমার সাথে কে কে একমত,0,sports
পাপন ভাউ আপনে পদত্যাগ করলেই হয়তো অনেক কিছুর সমাধান হয়েযাবে।,0,sports
"সানিয়া মির্জা আপনাকে আমার অনেক ভালো লাগতো,,,, অনেক খেলা দেখতাম,,, খুব খারাপ লাগতাসে",0,sports
পাপন যা শুরু করছে সেটা ঠিক না পাপন তো বহুৎ দুর্নীতি করছে তার বিচার কে করবে,0,sports
দুষ্ট গরু থেকে শুন্য গোয়াল ভালো।,0,sports
বিয়াদপ,0,sports
এত্ত করে আসে কেন 😭,0,sports
গালি দিয়েছে ভালোই করেছে মুশফিক কি তদের মার জামাই,0,sports
বাংলাদেশের ক্রিকেট দল এখন ধংসের পথে পাপনের জন্য,0,sports
ক্রিকেট কে বিদায় জানানো উচিত ছিলো কারন যেখানে দেশের মানুষই দুশমনের মত আঘাত করে সেখানে থেকেই বা কি লাভ?,0,sports
আমার পছন্দ পিলিয়ার সাব্বির,0,sports
সাকিব আল হাসান যেদিন মাঠে আসবে সেইদিন খেলা দেখবো,0,sports
অনেক ধন্যবাদ ভাই।আপনার প্রতিটি কথা সত্যি।আর যারা বাজে কমেন্ট করছেন তারা খারাপ কথা না বলে নিজেদের তথাকথিত পূণ্যবান হুজুরদের ইমেজ বাচানোর জন্য দোয়া খায়ের করতে পারেন আল্লাহতায়ালা আমাদের সকলকে হেদায়াত দান করুন।আমিন।,0,sports
রাসুলের অপমানে যদি কাঁদেনা তোর মন মুসলিম নয় তুই মুনাফিক রাসুল সঃ এর দুশমন।,0,sports
সালার পুত তোরে কি সোইতানে লারেচারেনি,0,sports
আমি মিরাজকে আগাই রাখলাম😍😍,0,sports
বাংলাদেশ ক্রিকেটকে ধ্বংস করার ষড়যন্ত্র করছে পাপন,0,sports
আবুল নাকি আপনে।,0,sports
এটা বেইমান চ্যানেল,0,sports
দঔনবাদ,0,sports
অনেক দিন পর।,0,sports
ভাইয়া আপনার কথা শুনে আমার আবেগে চোখের পানি চলে আসে,0,sports
যেটা ভুজলাম ভোলার ঘটনাকে ডাকার জন্য ক্রিকেট নিয়ে নাটক সাজান হইছে,0,sports
দেশ টা দালাল দিয়া ভইরা গেছেকিছু করার নাই,0,sports
রাইট বলছে,0,sports
এটা অপরাদ অ গালি দেইনাই,0,sports
Tahmid ভাই অনেক সুন্দর বিশ্লেষণ করেছেন <br />Love u bhai❤আপনি অন্য ক্রিয়া সাংবাদিক থেকে আলাদা বিশেষ করে দেব চৌধুরী। 😡😡😡 দেব ভাই খালি খালি খারাপ দিক খুঁজে বের করে,0,sports
একদম ঠিক কথা কয়ছেন আপনার সাথে আমরা একমত,0,sports
সিউর ক্রিকেট ম্যাচ প্রেডিকশন।😍 সিউর ক্রিকেট ম্যাচ রিপোর্ট দেয়া হয়,0,sports
পাপন তো অাগেই বলেছিল কারা ফিক্সিং করে তা খুব দ্রুত জানতে পারবেন হলও তাই হা হা হা,0,sports
পাপন এবার সব খেলা জয় করে দিবে খুব সহজে। পাপন মনে করে সাকিবকে ছাড়া দল ভাল মজবুত হবে।,0,sports
ওকে জাতীয় দলে নিলে ভালো হবে,0,sports
যে যা পারেন কয়েকটা পাপন গালী ক্রিয়েক করুন কমেন্টে। যা পরবর্তী তে কাউকে গালী দিতে সুভিধা হবে।,0,sports
ঝড়ে বক উঠছে আজ হঠাৎ করে। জাতীয় দলে কিছু করতে পারেনা ওরে কতো গুলো সুযোগ দিলো,0,sports
এখন বোর্ড পরিচালকদের বিরুদ্ধে তদন্ত করা প্রয়োজন,0,sports
বাঘের বাচ্চা ভাইয়া,0,sports
একজন পাপন হাজার সাকিব তৈরি করতে পারবে,0,sports
ছোটলোকের ছেলে,0,sports
আমাদের প্রধানমন্ত্রী সাকিব মাশরাফি মুশফিক মোস্তাফিজ এদের খুব পছন্দ করে স্নেহ করে তাহলে সরাসরি প্রধানমন্ত্রীর সাথে কথা বলা উচিত কারণ দিন শেষে ওনার হস্তক্ষেপ ছাড়া কোন কিছু হয় না,0,sports
অডিও তে কাজ হবে না ভিডিও চাই ভিডিও,0,sports
মুশফিকুর রহিম এর ভক্ত গুলা কই হাত তোলো,0,sports
সাকিব ভাই কে দল চাই,0,sports
গান কই,0,sports
কেসিনো সম্রাট পাপনের পদত্যাগ চাই। এই জুয়াড়ির কারণে বাংলাদেশের ক্রিকেটের আজ এ অবস্থা,0,sports
সাকিবের ক্ষমা নাইপাপনের মাংস খাই😹,0,sports
খারাপ সময়তো যাবে তুমি (পাপন) মিয়া তলে তলে টেমফু চালায় লে🤬🤬,0,sports
জনাব আজহারী সাহেবের অন্ধ ভক্তদের কাছে আমার কিছু কথা তোমরা তোমাদের বিবেককে সজাগ করে এগুলা পড় আর বলো কথাগুলা জনাব আজহারী সাহেব ঠিক বললো না ভূল বললো। তারাবির নামাজ রাকাত পরলেও হয়ে যাবে। নাউজুবিল্লাহ । এই জঘন্য ফতোয়া এই জ্ঞান পাপীর আগে আর কোন আলেম কখনো দিয়েছেন বলে আমার জানা নাই। সুন্নতে মুয়াক্কাদা নামাজ না পড়লেও কোন গুনাহ হবেনা। নাউজুবিল্লাহ অথচ এমন ফতোয়া কোন ফাসেক ব্যক্তি ব্যতীত কোন নিম্নমানের আলেমও কখনো দিতে পারেনা। মহিলারা রাস্তা ঘাটে হাট বাজারে যেখানেই যাবে চেহারা ও হাত খোলা রাখবে কোন সমস্যা নেই। তার মতে চেহারার পর্দা করা কোনো জরুরী বিষয় নয়। নাউজুবিল্লাহ প্রজেক্টেরের মাধ্যমে মহিলাদেরকে বয়ান শোনানো জায়েজ। নাউজুবিল্লাহ তাহলে আপনি নিজেই মহিলাদের প্যান্ডেলে গিয়ে বয়ান করলেই তো পারেন। পর্দার দরকার কি? রসূল সাঃ মক্কী জীবনে টেষ্ট ইনিংস খেলেছেন আর মাদানী জীবনে ছক্কা মেরেছেন। বল বাউন্ডারির বাইরে পাঠিয়েছেন। নাউজুবিল্লাহ আচ্ছা ভাই আজহারী! আপনি কি রসূলের জীবনকে ক্রিকেট খেলার মাঠ মনে করেছেন নাকি? রসূল সঃ এর বডি ছিল বডি বিউল্ডারদের মত সিক্স প্যাক। নাউজুবিল্লাহ খাদিজাতুল কুবরা হলেন তিনবার তালাক খাওয়া বৃদ্ধা মহিলা। তিনি ছিলেন পৌঢ়া। ইনটেক বা ভার্জিন ছিলেন না। আসতাগফিরুল্লাহ । কোনো হাদিসের কিতাবে খাদিজাতুল কুবরা রাঃ এর তালাকের কথা পাওয়া যায় নি হাদিসে শুধুমাত্র বিধবা কথাটি পাওয়া যায়। আল্লাহ্ মাফ করুন। অথচ রাসুল সাঃ খাদিজাতুল কুবরা রাঃ কে তাহেরা বলে ডাকতেন। যার অর্থ হল পুত পবিত্রা নারী। তাঁর জীবদ্দশায় আল্লাহ তায়ালা তাকে সালাম পাঠিয়েছেন। আল্লাহ ও রসূল সঃ এর শানে আবে হালা শব্দ ব্যবহার। আলী রাঃ শানে বেয়াদবীঃ মদ খেয়ে মাতাল হয়ে নামাজে দাঁড়িয়ে মাতলামি করে । নাউজুবিল্লাহ এসব বিবেকহীন কথা বলার পরেও যারা আজহারিকে নির্দোষ প্রমাণ করতে উঠে পড়ে লেগেছে আলেম ওলামাদেরকে গালাগালি করতেছে তারা গন্ড মূর্খ ছাড়া আর কিছুই নয়। উনি ওয়াজের মাহফিলে ছায়া ছবির গান গেয়ে স্রোতাদের বললেন আলহামদুলিল্লাহ বলতে গান শুনা গান গাওয়া গান গেয়ে আলহামদুলিল্লাহ পড়া কি জায়েয???,0,sports
ভাই ক্রিকেট মাঠে কেমনে ১০০তে১০০??১১০ইনিংসে একটা ১০০নাই। গড সব ফরম্যাট মিলে ২৫ করে।খেলবে কি নারী নিয়ে ব্যস্ত।,0,sports
তোদের মত পাগলরা বাংলাদেশ,0,sports
ক্রিকেটেরা ক্রিকেটকে নষ্ট করতে চায় না। ক্রিকেটকে নষ্ট করছেন আপনারা। আর আপনি যে ভাবে কথা বলছেন বুঝাই যাইতেছে কেমন সম্মান পায় ক্রিকেটেরা। গলা নামিয়ে কথা বলেন আপনি।,0,sports
ভাইয়া আমাদের সাকিব ভাইয়াকে আমার মাসের জন্য না সারা জিবনের জন্য হারাচ্ছি কারন এভাবে সাকিব ভাইয়াকে বাদ দিতে পারতনা সাকিব ভাইয়াকে ফাসিয়ে বাদ দেওয়া মনে সারা জিবনের জন্যা বাদ দেওয়া আর সাকিব ভাইয়া আপনে বাংলাদের হয়ে আর খেলবেন না অন্য দেশের হয়ে খেলেন আমি বা আমরা আছি আপনার সাথে জে দেশে সোনার চে লোহার দাম বেসি সে দেশে আপনার খেলার কোনো খেলা দরকর নাই। (সেলুট সাকিব বস),0,sports
জুতা দিয়া বাইরামু।তোরা কাম পাস না?সরকারের কাছ থেকে এভাবে টাকা নেওয়ার কনো মানে হয়না,0,sports
ক্রিকেট নিয়ে তামাশা শুরু হয়েছেএবার ভারতে গিয়ে বিশাল বাম্বো খাবে সিউর।,0,sports
তুই কনো কথা বলবিনা পাপোন,0,sports
মুশফিককে গালি দিছে তো কি হয়ছে খাহিনি করস পিছনে নিস কেন উনাকে তুই শালা তো দেখতে গাযাটির মতো সেলেব্রিটি জগতে থাকলে গালা গালি ভাল মন্দ সব শুনতে হয় তাই বলে তুরা এরকম কেন করবি,0,sports
আমাদের বিশ্বনবী আমাদের দয়াল নবী আমাদের মায়ার নবীকে গালি দিলে জলে না আর মুশফিক কে গালি দিলে অন্তর পুড়ে যায় না শালার বাবা খোর,0,sports
বাংলাদেশের প্রথম সুপারস্টার ছিল আশরাফুল তাকে ইন্ডিয়ান দালালের খপ্পরে পরে আমরা হারাতে হয়েছে এখন আমরা হারালাম সাকিব কে ঐ ইন্ডিয়ান দালালের খপ্পরে পরে আমার হিসেবে ইন্ডিয়া কে বহিষ্কার করা উচিত আর পাপন কে কিছু বলার নেই কারণ ওনার সামান্য তম লজ্জা থাকলে ও পদত্যাগ করতেন,0,sports
এই রানা এবং মাহমুদুল হাসান অনেক ভালো বল করে,0,sports
শাকিবকে খেলায় চাই,0,sports
"সাব্বিরের উপর সবাই এতো ক্ষিপ্ত কেন!!উনি কি মানুষ খুন করছে!!! কারো টাকা চুরি করছে!!! <br />বিসিবি সাব্বিরকে শুধু শাস্তিই দিয়ে যাবে ভাল আর করতে পারবে না।<br />বাবা যদি ছেলেকে কোন ভুলের জন্য শুধু মানসিক শারিরীক নির্যাতন করে তখন সে ছেলে কখনই ভাল হয় না। <br />সাব্বির প্রতিবার শাস্তির পর আবার তার খারাপ রুপ প্রকাশ পায় কেন তার একটাই কারন তাকে শুধু ভুলের জন্য শাস্তিই দেয়া হয়, কখনো তাকে বাবা মায়ের মত ভালবাসা দিয়ে বুঝানো হয় না।",0,sports
তোমাদেরকে আগে ঠিক করো তারপর অন্যজনকে এটা ওটা বল বাট মাই ফেভারিট প্লেয়ার সাব্বির রহমান আই লাইক সাব্বির রহমান,0,sports
পাপনের কাম মিন গোডফার পাপন,0,sports
পাপনের পদত্যাগ চাই এবং আমার নতুন ইউটিউব চ্যানেল সাবস্ক্রাইব করুন প্লিজ প্লিজ প্লিজ,0,sports
পাপনকে পদত্যাগ করা হোক,0,sports
নিশ্চয়ই এখানে হাত আছে 😃😃😃 শালা একটা বড় দানদা বাজ বাটপার,0,sports
একে জাতীয় দল থেকে বাদ করে দেয়য়া উচিত,0,sports
ভিডিওয়ের ফিনিশিংটা দেখে চোখের জল আটকাতে পারি নাই 😣💔😭😭,0,sports
কন্ডম ব্যবহার করেছে। তাই ক্ষমা করে দেওয়া হোক।<br />যাদের খাড়া হয় তারা লাইক করেন। <br />হ্যাপী দেখতে হেব্বি।,0,sports
তামিম ইকবাল নাই তাই জিততে পেরেছে কি বলেন ভাইয়েরা,0,sports
সাকিব ভাইকে দেখে খেলা দেখা শুরু এবং বুঝা।সাকিব ভাই শুধু মাস না দরকার হলে আর কোনো দিন দেখবো না খেলা।,0,sports
এদের বেতন কমিয়ে দেন।।।।,0,sports
পাপন সাহেব সব যুক্তিযুক্ত কথা বলছে। প্লেয়ারদের সুবিধা বেশি হইছে। আর কত?,0,sports
অবশেষে ওয়াটসনের ব্যাটে রান খরা কাটলো অভিনন্দন রংপুর রেঞ্জার্স❤️,0,sports
তুই শালা আশরাফুলের সময় কেমন কথা কইলে আর এখন কি কস সাকিব এর জন্য দু:প্রকাশ ভাইক্রিকেট কে ভালোবাসি তবে তোদের মত দালাল এর জন্য আজ এই অবস্তা,0,sports
বাল সাল ভিডিও,0,sports
দন বঙ্গবন্ধু টুর্নামেন্ট,0,sports
খুব কষ্ট পেয়েছি সে দিন।,0,sports
পাপনের মেয়েকে রিপন এর কাছে পাটিয়ে দেন😂😂,0,sports
তরা কি সকালে নাস্তা না খেয়ে মাঠে নামছ মনে হয় তেমনি ঠিক মতো কেচ দরতে পারছ না,0,sports
খতিব অনেক ক্ষতি,0,sports
"আমার কাছে মনে হয়েছে,&quot;এবার আমি নয় আমার ব্যাট কথা বলবে&quot;,,সেটা বোঝাতে চেয়েছেন সাব্বির।আর খেলা শেষে এই এক উদযাপন নিয়ে এত কথা উঠছে।আমরা সহজে পজিটিভ থিংকিং করতে পারিনা।এটাই সমস্যা",0,sports
ফারুখ ঠান্ডা হইয়া গেসে😂 আর এ কেমন খেলা বা দুষ্টামি? ফারুখ যেমন একটা খাইসে ঠিক এমনি একটা বয়রা তার খাওয়া উচিত যে এমন খেলা বা ফাজলামি শুরু করসে।,0,sports
পাপনকে বিতারিত করা হক,0,sports
এরা বিপিএলেই বাল ফালাইতে পারে জাতীয় দলে গেলেই হাইগা দেয়,0,sports
পাপনের গালে গালে জুতা মারো তালে তালে👞👞👞👞👞,0,sports
হেতে নিজে আছে এটার সাথে জডিত,0,sports
মুজিব কাকু উপর থেকে বিপিএল দেখতেছে ভালই চলতেছে বলতেছে কাকু,0,sports
মিথ্যাবাদী তোমার বাবার নাম তুমি ডুবাইছো ।,0,sports
সৌম্য রানে ফিরেছে প্রতি পক্ষের খবর আছে,0,sports
ব্রেকিং নিউজঃ এই নিউজটি যে ছাড়ছে সে আত্মহত্যা করছে,0,sports
ধন্যবাদ সত্যি কথা বলার জন্য। দোয়া রইলো।,0,sports
আমি মনে করি সব পাপনের ষড়যন্ত্র।আমার বক্তব্য কে কে সমর্থন করেন,0,sports
শালা বাংলাদেশ রে,0,sports
ক্যামেরা কিলিয়ার না জি টিভি সরি,0,sports
পাপোন কে পিটিয়ে মারা দরকার,0,sports
জনির বিডিও আর দেখবো না ্,0,sports
তাসকিনকে পরিচর্যা করলে আমাদের ক্রিকেট উপকৃত হতো।,0,sports
আসালামুআলাইকুম সভাই কেমন আছেন আমারদের দেশের মানুষের ভালো ভাষা দেকলে অবাক লাগে আমাদের নবী করিম হজরত মোহাম্মদ কে গালিগালাজ করতে ছে এই গোলা পথিবাত করছেনা কিন্তু মুসিরিক কে গালির দেওয়া র কারণে একটা ছেলের কলার টানাটানি কি ওদভুদ🇧🇩,0,sports
ভারতের সাথে ম্যাচ খেলতে না পারার জন্য ভারত এ কাজ করেছে আগে যেমন ইলিয়াস সানিকে নিষিদ্ধ করেছে এখন ইলিয়াস সানি সাকিব ভারতের সাথে খেলা হলে ভারতের মাঠে ভারত হারবে। তাই এ কাহিনী করে,0,sports
আন্দোলনের বলি সাকিব আল হাসান,0,sports
ভাইটার আহাজারী দেখে মনে হলো সত্যি সত্যি বলছে।,0,sports
বরো জুয়ারি শালায়।,0,sports
চোখের পানি ধরে রাখতে পারলাম না😭😭😭,0,sports
"এটার নাম বাংলাদেশ.যে জায়গায় তামিম,মুশি রা ব্যাট নাড়াতে পারছেনা সে জায়গায় সাব্বির ১ সেঞ্চুরি এবং সিরিজ এর ২য় টপ scorer.সাব্বির ব্যাট ভাল করেছে বলে ১০০ রানে অল আউট হয়নি বাংলাদেশ.celebration আছে,মিরাকল,উদ্দিপনা বলেই ক্রিকেট এত জনপ্রিয়.সাবাস সাব্বির এগিয়ে যাও. সমালোচক এর কাজ জয় পরাজয় এ উল্টো দিক কথা বলা.Go ahead sabbir.<a href=""http://www.youtube.com/results?search_query=%23best"">#best</a> of luck bangladesh for test seriz",0,sports
আল্লাহ কখন মানুষ কোন জায়গায় নিয়ে যায় বলা যায় নাসির সিনেমা দেখা টা ছেড়ে দিয়েন সিনামার টাকা গুলো মসজিদ মাদ্রাসায় দান করুন আল্লাহ আরো সম্পদ বৃদ্ধি করবে।,0,sports
হ্যািপ ঠিক কাজ করেছে।এই মত আমি জীবনে ভালোবাসা পাইনি রুবেল পেয়ে ছেরে দিলো।আমি হ্যাপিকে অনেক ভালোবাসবো।হ্যাপির দুংখ কষ্ট ভুলে দিবো ok,0,sports
আপনার অপেক্ষায় ছিলাম,0,sports
তাছকিন একটা খারাপ পোনা নোটির পোলা,0,sports
সাকিব আল হাসান না তাকলে কেলা দেকে লাব নাই আগামী তারিখ তেকে বাংলাদেশের কেলা দেকা বন্ধ,0,sports
তাসকিন একটা বেয়াদব আর এটাই প্রমানিত,0,sports
রুবেল তুমি এভাবে মানুষকে বোকা বানাতে পারবে না আসলে অপরাধী,0,sports
চট্রগ্রামের জন্য শুবেচ্ছা ইবা আরার চিটাইংগে,0,sports
আমার মতে এই দেশের এিকেটের মুকে মুতি চলে যাওয়ার দরকার ছিলো সাকিবের।।।,0,sports
ধবংস করাটা খুব সহজ কিন্তু একটা সাকিব গড়া খুব কঠিন তোমার সাথে যা হয়েছে তা জাতি কোন দিনও ভুলবেনা 😔😢😭 🤘✌️💪,0,sports
যে যাই ই বলুক আমি সিয়োর বাংলাদেশের ক্রিকেট কে ধংস করার পায়তারা চলছে।আমি সাকিব কে বলবো ভাই মাসের জন্য নিসিদ্দ্ব হওয়ার কাছ থেকে তুমি সব ধরনের ক্রিকেট থেকে অবসর নাও। আর তোমার দায়িত্বটা পপকন কে বুঝিয়ে দাও।,0,sports
বেতন আরো দুই লাখ বারিয়ে দাও🤣🤣🤣🤣🤣,0,sports
পাপনের কথা শুনে আমি আমরাও শক,0,sports
সাকিব না থাকলে বাংলাদেশ দল বেটারি ছাড়া মোবাইলের মতো। তাইতো?,0,sports
এ বেটা তুই একটা খেলোয়ার<br />পতিতার কাছে গেলি কেন??? বল রুবিল্লাহ,0,sports
আমি চাই খুলনা আর চট্টগ্রাম ফাইনালে যাক।,0,sports
ওর মত প্লেয়ার বাংলাদেশ দলে কেন খেলে তাই ত বুঝি না ।হালা ছাগলের তিন নম্বর বাচ্চা।,0,sports
দর্শক বলবে তাই বলে এমন ব্যবহার করবে এইটা ঠিক না।আজ আবুল পোলাপাইন বলে এমন করে পারছে।শালার।,0,sports
সাকিব ত বিসিবি কে জানাইচে তাহলে এত বড় সাজা কেনোসাজা পেতে বিসিবি অ পেতে হবে,0,sports
রাজশাহী সাপোর্টাররা আমায় সাব করুন 💕💕💕,0,sports
মিডিয়া আরো লবন মরিচ দেয়।🇧🇩🔥,0,sports
রাজশাহী এবার কাপ নিবে একমত কে কে,0,sports
না না না মানি না।। এটা কি ধরনের কথা।। হায়ানারা ইচ্ছা করে এটা করসে।। এটা দেশের মানূষ এটা মানবে না।,0,sports
এই সব বিসিবির দোষ। সে নিশ্চয় ইন্ডিয়া থেকে টাকা নিয়েছে। একানে সাকিবের কোনো দোষ নেই।অতএব সাকিবকে জানাই সালাম।একানে যদি বিসিবির দোষ না থাকত তাহলে এরকম টা হতনা।,0,sports
পাপনের পদত্যাগ চাই অ্যান্ড সাকিব কে দলে আনা চাই,0,sports
রুবেলকে টুকায় টুকায় লাগে দেখতে,0,sports
এসো সবাই ওয়াক্ত নামাজ আদায় করি,0,sports
এটা ভারতের সাথে সেচ্ছায় হারার একটা ইস্যু। খোজ নিয়ে দেখুন পাপন কাক্কু এর সাথে সরাসরি জরিত। তাই পাপন হঠান বাংলাদেশ িক্রকেট বাচান,0,sports
রাসেলের সাপোর্ট গুলা কই,0,sports
জিম্বাবুয়ের খেলোয়াড়েরা টাকা ছাড়াই খেলতে পারেআর আমাদের খেলোয়াড়েরা রাজপুত্রের মতো থেকে ও এমন আচরণ করে! লজ্জা হওয়া উচিত।প্রকৃত দেশপ্রেম থাকলে এমন হতো না।,0,sports
আল্লাহ সবাইকে হেদায়াত দিন,0,sports
আপনি পদত্যাগ করেন,0,sports
আমার নিঃশ্বাসে প্রশ্বাসে আছে তামিম ইকবাল খান এবং ঢাকা প্লাটুন,0,sports
এটা বিএনপি জামাতের চক্রান্ত কাক্কু মতে 😂😂,0,sports
আমি অনেক খুশি পাপন ভাই জার বেতন লাখ আবার বলে বেতন বারান,0,sports
বাংলাদেশে নতুন কিছু সাংবাদিক আছে ওরা সহজ সরল মানুষ গুলাকে নাকিছুবানি না খাওয়াইয়া ছাড়ে না। আমার বালের সাংবাদিক।,0,sports
পাগল হইলি না কি রে ভাই পালতু বিডিও দেস কেনো,0,sports
সাকিব এর নিষিদ্ধ হবার খবর যখন রাত এর দিকে দেখলাম আমি যেন হতবিহ্বল হয়ে গিয়েছিলাম কিছুক্ষনের জন্য। সারাদিন এ চ্যানেল ও চ্যানেল করে বেড়িয়েছি কখন আসল খবর টা শুনবো। সারাদিন অস্থিরতায় কেটেছিলো আর যখন সত্যি সত্যি শুনলাম নিষিদ্ধ এর কথা তখন আসলে আমি বাক্রুদ্ধ । সাকিব এর সেই ছলছল চোখ যেন আমাকেও কান্না এনে দিয়েছিল। সাকিব এর খেলা হয়েছে আর আমি দেখিনাই এমন হয়নাই কোনদিনসে যে লীগ হোক আর ছোট কোন ম্যাচ হোক।মাঠের সাকিব যে কত বড় জিনিস সেটা বলে বোঝাবার নয়। সাকিব বিহীন বছর খেলা দেখার আগ্রহ ই হারিয়ে ফেলবো ।,0,sports
সাকিব আল হাসান নেই তাই আমিও নেই,0,sports
একটা মানুষের উপরে কখনো একটা দল চলতে পারেনা সাকিব আল হাসান যদি অপরাধ করে তার অবশ্যই সাজা হওয়া উচিতসে ছাড়া যে দল চলবে না এটা কখনোই ভাবা উচিত না।,0,sports
প্রিয় খেলোয়াড় মাহমুদুল্লার জন্য খারাপ লাগতেছে বিদেশীদের উপর ভরসা করে সব দিক থেকে আমাদের দেশটা তলিয়ে যাচ্ছে মিস ইউ বাংলাদেশ এত এক্সসাইটিং একটা ম্যাচ বাট বালের কমেন্ট্রি মুশি কোলে উডি গেছে,0,sports
পাপন নান্নুর বাদ দেয়া এখনই দরকার।কে কে একমত লাইক দিন,0,sports
আমরাহ চাই সাকিব আমাদের বাংলাদেশের টিমে খেলুক কিন্তুু ওর শাস্তি কমায় দিলে বালো হয়,0,sports
আশা করছি সে বিপিএলে পারফর্ম করে জাতীয় দলে চান্স পাবে।আর বিসিবির সকল সদস্যদের বলছি একটু প্লেয়ারদের উপর নজর রাখুন। কে কিরকম খেলছে।আর পারফর্মারদের সুযোগ করে দিন।শুধু সৌম্য আর সাব্বিরকে দয়া দেখিয়ে লাভ নেই।বাংলাদেশে ভালো প্লেয়ার অনেক আছে।,0,sports
ভাই মিথ্যা শিরোনাম দেন কেন? এখানে রুবেলের গান কোথায়?৷ আপনি একটা ফালতু।,0,sports
মা বোনকে গালী শুনাতে খুব ভালো লাগে মনে হচ্ছে তাই না,0,sports
সাকিব ছাড়া বাংলাদেশ ক্রিকেট টিম একদম অচলকি বলেন সবাই।,0,sports
এ,0,sports
তথাকথিত ভবিষ্যৎ এস সমস্ত বেয়াদব তারকাদের জাতীয় দলে আর দেখতে চাইনা।,0,sports
সোনার চেয়ে দামি। বালের দামি,0,sports
আমাদের দেশে এইসব আবাল জিনিস নিয়ে মানুষ কামড়াকামড়ি করে।।।।।এটাই বাংলাদেশ।।।।।আজাইরা কাজ কাম।।।।,0,sports
এখানে অনেকেই না বুজে একটা কথা বলছেন যে ক্রিকেটাররা আমাদের টাকায় চলে। আসলে ব্যাপারটা এমন না। ক্রিকেট বোর্ড একটা ইন্ডিপেন্ডেন্ট বডি। এটা টেক্সের টাকায় চলে না। এটা তার নিজেস্ব টাকাতেই চলে। আর বোর্ডের টাকা আসে স্পন্সর সত্ত্ব বিক্রি টিকেট ইত্যাদি থেকে। সো আসলে খেলোয়াররা বোর্ডের টাকায় চলে। পাবলিকের টাকায় না। উলটা তারা আর সব মানুষের মত ইনকাম ট্যাক্স দিয়ে থাকে।,0,sports
যোগ্য বাবার যোগ্য সন্তান! সবগুলো দাবির সুন্দর জবাব দিছেন!এত সুযোগ সুবিধা পাওয়ার পরও এক একজন কোন বা ল খেলে দেখিত আমরা সবই! আফগানিস্তান জিম্বাবুয়ের নূন্যতম কোনো সুযোগ সুবিধা পায় না তার পরও ওদের চেয়ে ভালো খেলে! লাগবেন না এইসব বেয়াদব হনুদের আপনি ইয়ং দের নিয়ে নতুন করে শুরু করেন এইটাই বেস্ট হবে!,0,sports
আমার মনে হয় পাপন জড়িত,0,sports
নতুন একটি নাটক সবাই দেখবেন,0,sports
দেখে দেখে পড়ে তার মানে অন্য কেউ এই কথা গুলা লিখে দিছে। নাটক নাটক সব নাটক।,0,sports
আরে এর সাথে তো পাপন নিজেই জরিত।,0,sports
বাংলাদেশ এখন শাকিব ছাড়া কেমন খেলেএটাই দেখার বাকি এখন,0,sports
শালারপুত মিছা কথা কস ক্যান চ্যানেলের প্রাইভেসি বেড়ানোর লাইগা,0,sports
"এসব খারপ মেয়ে,,রুবেক ভাই তুমি তারতারি কেটে পরো",0,sports
মুস্তাফিজুর রহমান অবশ্যই পোরুনো ছন্দে ফিরবে।,0,sports
এইখানে পাপনের চালবাজি,0,sports
ঠিক বলেছেন,0,sports
এখানে কার সাপোর্টার বেশি দেখা যাক?? কমেন্ট করো তুমি যাকে সাপোর্ট করো।,0,sports
বিসিবি বস বলতে আমরা যাকে দেখি সে হচ্ছে সাবেক যার সময়ে বিসিডি সবচেয়ে বেশি আলোর মুখ দেখেছে আর এখন তো এগুলা দালাল,0,sports
সারাদিন ইউটিউবে সেক্স ভিডিও যারা খুজে কিন্তু দিন শেষে কোনো ভিডিও পায় না তারাই এ ভিডিও গুলাতে ডিসলাইক মারেলাভ ইউ বো😍,0,sports
পরিশেষে ইমরুল কাসের হাতে বি পি এলের ট্রফি টা উঠলো 😄😄😄😄😄,0,sports
জিবনে একটা বিশ্বকাপ জিততে পারে নাই আবার বেতন বাড়াতে হবে কোন জন্যে। এদের থেকে মেয়েরাই ভাল খেলে তাদের বেতন বাড়ানো হকো,0,sports
ট্রাজেডি,0,sports
আফগানিস্তানের সাথে বাংলাদেশের হার এইটা মেনে নেওয়া যায় না। ছি,0,sports
টাকা আর টাকা ক্রিকেটার রা পাগল হয়ে গেছে,0,sports
জীবনে বার খুব কষ্ট পেয়ে কেঁদেছি ম খুব কষ্ট লেগেছিল যে দিন প্রথম ভালবাসার মানুষটাকে হারিয়ে ছিলাম কিন্তু চোখের পানি এতটা ঝড়েনি আজ য় বার মত করে কাঁদলাম মনের মধ্য এত বড় একটা আঘাত পেয়ে কাঁদব সেটা কখনও ভাবিনি তাও সাকিব ভাইয়ের জন্যএখন মনে হচ্ছে আমার ভালবাসার মানুষটার চেয়ে অনেক বেশি সাকিব ভাইকে ভালবেসেছি যার জন্য চোখের পানি ধরে রাখতে পারছিলা এইটাই হল প্রকৃত ভালবাসা💔,0,sports
সাব্বির রুবেল ও নাছির কে কঠুর শাস্তি বেবস্থা নেওয়া হোক তাড়া দেশের কলংক নারী কেলেঙ্কারির দিয়ে পচিয়ে ফেলছে দেশটাকে এরা,0,sports
মাগুরার সর্ব সাধারণ জনগণের পক্ষ থেকে ধন্যবাদ ভাই আপনাকে,0,sports
বাঙালি শুধু হুচোকে নাচে।।আগে শোনসে কি করছে তা না পাপন হারামি।।।না জানিয়ে দল পরিবর্তন করবে এটা দোষের না এটাও পাপন হারামি দায়ী!!! কত ভালো বছর আগের কাহিনী নিয়া মাতামাতি করছে সেটার দোষ কার??পাপন;সাকিব,0,sports
"সেঞ্চুরি করে সাব্বির যেভাবেই উৎযাপন করুক, ব্যাট হাতে বেয়াদবি করুক আপত্তি নাই। মাঠের বাইরে শৃঙ্খলা মানলেই হলো।",0,sports
পাপকে নয় পাপনকে ঘৃনা করুন😐😐,0,sports
জিতবে কুমিল্লা মাতাবে দেশ,0,sports
সাকিব তোমার ভয় নাই,0,sports
ভাই কষ্ট লাগে কিছু করার নেই। মনে হয় কী যে করতে বলে বোঝাতে পারবো না।,0,sports
শাকিব আমার প্রিয় খেলোয়ার,0,sports
পাপন তোমাকে বলি এটা আশাফুল না ওনি সাকিব বিশ্ব এক নাম্বার আছে তুই কি করলি কোওা,0,sports
"ওর উৎযাপন দেখে,বুঝাই যায় ওরা দেশের জন্য খেলে নাকি নিজের জন্য খেলে",0,sports
তাজকিনকে চর মারার প্রতিযোগিতা হক,0,sports
ভাই ভিডিও না বানিয়ে আনন্দলন করেন,0,sports
"নায়লা নাইমের সাথে রেগুলার খেলেও মন ভরেনা, সানিয়া মির্জাকে চেখে দেখতে চায়",0,sports
এইভাবে ছেলেটাকে হেনস্থা করা ঠিক না।যারা ওকে ধরছে সব ব্যাটা শালারা গাঁজাখোর। হুজুগে বাঙ্গালী যা হয় আরকি 🤬🤬,0,sports
ওরা চাইলেই করতে হবে বিসিবির কোনো দায়িত্ব নেই।,0,sports
সাকিবের উচিত এখন অন্যায়ের কাছে মাথা নত করা ঠিক হবে না। সবকিছু পাপনের চালাকি।,0,sports
লক্ষ্য লক্ষ্য টাকা কামাইতেছে তাও পেট ভরে না সুখে থাকতে ভূতে কিলায় কি বাল খেলতেছে সবগুলোরে বদল করে নতুন পতিভাদের সুযোগ দেওয়া হোক,0,sports
এটাও কি বিএনপি জামাত দায়ি ? ষরযনএ কেন বলা হচ্ছে,0,sports
আজ থেকে আর খেলা দেখবো না জত দিন শাকিব না ফির বে😞😞,0,sports
ভালো ইনিংস,0,sports
বুঝলাম না ওহায়াব রিয়াজ এর বয়স বাড়ছে আর বলের চমকটাও দিন দিন বাড়ছে বাহ আর আমাদের মোস্তাফিজ দিনকে দিন হারিয়ে যাচ্ছে।,0,sports
এটা কি হাইলাইটস?? গেইল কিভাবে আউট হলো। আবালদের দিয়ে হাইলাইটস করালে এই অবস্থাই হবে।,0,sports
বলিংয়ে আরও কৌশল রপ্ত করতে হবে ইয়র্কার ওয়াইড ইয়র্কার ইন সুইং স্লোয়ারের মতো বিষয় গুলো নিয়ে কাজ করলে সাফল্য পাওয়া যাবে আশা করি।,0,sports
আমরা বাঙ্গালীর জত আছে বাল ছাল নিয়া পইরা থাকি।,0,sports
পাপনের পদত্যাগ চাই। জোয়ারির পদত্যাগ।,0,sports
পাপন সালাউদ্দীন না গেলে ক্রিকেট ফুটবল শেষ,0,sports
"কোরআনের পাখিদের জন্য এই ভিডিও টি < ="": "">: < >",0,sports
খেলা হলো খুলনা আর চট্টগ্রাম আর এরা দেখায় সিলেট আর রাজশাহীর গাঁজা এরা খাইনি গাঁজা এদের খাইছে।🤣🤣🤣🤣🤣,0,sports
শচিন এর বাড়ির সামনে তার ফ্যান গুলা আগুন জায় জুতা পারে আর 🇧🇩😁😁😁হাসসো কর,0,sports
আপনার দেখে ভাল লাগলো আর আমি এইটা দেখে বুঝতে পারলাম যে আপনার জন্ম হয়েছে আপনার বাবার পু কি দিয়ে কারন অবশ্যই কোন না কোন নাস্তিক আপনার বাবার পু কি মেরেছে যার ফল স্বরুপ আপনি এসেছেন । আমি কি ঠিক নাকি আমি ঠিক,0,sports
এটা সাজানো নাটক মাত্র এতে বুজা যায় ইন্ডিয়া বাংলাদেশকে ভয় পায় তাই সব সময় নেত্রীত্ব শূন্য করতে চায় পাপন হলো নাম্বার ওয়ান চুতিয়া পাপন এর সাথে সরাসরি জরিতএই তিনজন হলো চাটুকার,0,sports
নাটের গুরু পাপন,0,sports
"আর যতই পাকনামি করোনা কেনো,সাব্বিরের মতো আাগুন ঝরানো ব্যাটিং বাংলাদেশে আর একটাও পাওয়া যাবে না,,যদিও তামিম ইকবাল আছে, তারপরেও সাব্বির সেরা,,,",0,sports
এই সব ভন্ডামি বন্ধ কর পাপন আমরা ভাল করে জানি সিলেট কে উপরে উঠতে দিবে না,0,sports
মুশফিকুর রহিম কে গালি দেওয়ার মত এরকম লোক আমাদের বাংলাদেশে আছে আমি প্রথম দেখলাম কারণ মুশফিক ভাইয়ের মতো পিলিয়ার আমাদের বাংলাদেশে এখনো হয়নি আর হবে কিনা তাও সন্দেহ বর্তমানে একজন প্লেয়ার আছে আমাদের নির্ভরযোগ্য মিডল অর্ডার। আজও আমরা তাকে নিয়ে স্বপ্ন দেখি আর মুশফিক ভাইকে আমার পক্ষ থেকে অবশ্যই থাকবে যে আমাদের মধ্য থেকে কেউ না কেউ একটা গালি দিয়েছে ভাইয়া আপনাকে আমি আমার অন্তস্থল থেকে আপনাকে অনেক দুঃখ প্রকাশ করছি আপনি সবাইকে মাফ করে দিবেন আমাদেরকে ভালো থাকবেন।,0,sports
পাপন সাহেব দায় এড়ানোর চেষ্টা করতেছে এইখানে।,0,sports
সাকিবকে দরকার বাংলাদেশ দলের,0,sports
আপু তুমি চালিয়জও আমরা আচি তোমার শাতে,0,sports
পারে না খেলতে আবার মেজাজ দেখাই বোকা,0,sports
ক্রিকেট বাংলাদেশের প্রাণতাই আমাদের সবার এক হয়ে প্রতিবাদ করা উচিৎ✌,0,sports
আমার মনে হয় নুরুল হাসান সোহানকে জাতীয় দলে নেওয়া উচিত। সে কিপিং গত বছর ধরেই দেশসেরা। তার কিপিং কুইন্টন ডি কক জস বাটলার ব্র‍্যাড হ্যাডিন মানের। শুধুমাত্র ব্যাটিং এর কারণে দলে নেওয়া হতো না। কিন্তু ইদানীং মুশফিকের বাজে কিপিংয়ের কারণে বাংলাদেশ অনেক হারতেসে। আর নুরুলও ভালো ব্যাটিং করতেসে। তাই আমি নুরুল হাসান সোহানকে ন্যাশনাল টিমে চাই।,0,sports
দারুণ 🌼🌼💙💙💙,0,sports
আপনাদের সকলের সাথে আমিও একমত,0,sports
"দোশ বি রুবেলের একা ছিলো,,,,",0,sports
হাহাহা!আগেই বুঝতে পেরেছিলামআন্দলনের কারনে যে কেউ বাদ পরতে পারে😁😁😁,0,sports
আমরা আগের মতো বিপিএল খেলা দেখতে চাইমালিকানাশুধু বিসিবির দখলে চাই না।।,0,sports
গালিগালাজ না করে সবাই মিলে রিপোর্ট করুন। পাগল মুক্ত ইউটুব চাই!,0,sports
নান্নু সুজন দুর্জয় কে বাদ দিয়ে নতুন কমিটি গঠন করেন,0,sports
একজন সাধারণ পাপলিগ কে এ ভাবে হেস্ত নেস্ত করে মুসফিক তাকে এত পাওয়ার কে দিসে।সাধারণ পাপলিগ রা খেলা দেখ ওদের পেট চলবে না,0,sports
পাপনকে পদত্যাগ করা উচিত না হলে সাকিব ইন্ল্ড হয়ে খালবে,0,sports
মুশফিক কে গালি দিছে এটা কোন অপরাধ নয় বরং তাকে বুঝিয়ে বললেই হয় একটা মানুষ সবার কাছে প্রিয় হতে পারে না,0,sports
বিশ্বের স্পীড স্টার বোলার ক্যাসিনো খালেদ মাহমুদ সুজন সাপকে বিসিবি,0,sports
রাজশাহী এবার কাপ নিবে একমত আছেন কে কে?,0,sports
দশ ম্যাচ খেলে এক ম্যাচ ভাল করে তাই বালের খেলোয়ার,0,sports
রংপুর কে ধন্যবাদ দিলাম,0,sports
পাপন ভাইরে তর বয়স হইছে।আল্লা যা ভাই।,0,sports
বিসিবি সভা পভাতি পাপনেৱ জুয়া খেলাৱ ভিডিও ফাসঁ তো বিসিবি সভা পভাতি পাপনকে পদত্যাগ চাই,0,sports
কি রে রুবেল তুই জাল বাওয়া হেমা দিয়ে দিছছ।,0,sports
দেশের মানুষ কেন বিপিএল খায় না🤔🤔🤔🤔🤔🤔,0,sports
মুসফিক কি বাল ফালাইলো মুসা নাকি কি বালের প্লেয়ার ভাব চোদাই স্মিথের মতো বালছাল এজন্যই বছর খেলে ভালো কিছু করতে পারে না।,0,sports
ভাইয়েরা আপনারা কি একটা জিনিস খেয়াল করছেন এতদিন তো ম্যা ফিকশন কথাই আসেনি যখন তারা আন্দোলন করছে এরপর থেকে তো এসব ঘটনা গুলো না,0,sports
আমিও এমন উজ্জাপন করতাম।।,0,sports
এদের কে দলথেকে বাধ দেওয়া উচিত,0,sports
তামিমকে থেকে বাদ দিতে পারে বললেন দেখুন কি বললেন👉,0,sports
ফালতু কথা,0,sports
এটা ঠিক হয় নি,0,sports
ভাল লাগে যখন দেখি দেশি খেলয়াররা ভাল খেলে নির্বাচকরা যদি একটু গাজা না খেয়ে দেখে তাহলে দেশের জন্য ভাল কিছু হবে,0,sports
পাপন মূল হোতা।ওকে আজীবন নিষিদ্ধ করা হোক!!!,0,sports
হারলেও দুঃখ নাই পয়সা উসুল ম্যাচ ছিলো তবে সৌম্য আবাল কে ডেথ ওভারে বোলিং দেওয়া সবচেয়ে বড় বোকামি! খানকির বাচ্চায় যদি পাওয়ার প্লেতে কিছু রান করে দিতে পারত ম্যাচটা জিতা হত !! কিন্তু চারাল আবালে ক্যাচ শিখাইছে এত বড় ম্যাচে 😂😛😛😛😁😁😁,0,sports
সবচেয়ে মজা লাগে যখন সৌম্য সরকারের ব্যাটের টাইমিং সাউন্ড শুনি।,0,sports
পাপন কে দেকতে চাইনা আর,0,sports
নাসির কে কেনো জে টিমে রাখে আমি বুজি না এই হলো একটা ফালতু পিলিয়ার,0,sports
ইমরুল দলে না তাকা কারুনে কেলা এমনি হবে ইনসাল্লাহ,0,sports
পাপন একটা চুর দূরনিতি বাজ,0,sports
সাকিব ভাই আমার তোমার সাথে,0,sports
আজকে একমাত্র রাসেলের কারণে ম্যাচা জিতেছে।,0,sports
আল্লাহর গজব পড়ছে ক্রিকেটারদের উপর<br />আল্লাহ্ মাফ করো হেদায়েত দান করো,0,sports
আজ থেকে খেলা দেখা বন্দ।বায় বায় বাংলাদেশ????,0,sports
"তর প্রবলেম কি মাদারচুদ
",0,sports
বাংলাদেশের জাতীয় ফুটবল টিম যদি শুধু দক্ষিণ এশিয়ার মধ্যে সর্বোচ্চ জায়গাটা ধরে রাখতে পারতো তাহলে তোদের ক্রিকেট খেলা কুত্তা ও দেখতো না!!😡😡🖕🖕🖕 ভাব দেখে মনে হচ্ছে ওদের জন্মদাতা বাপকে গালি দিছে🤔🤔 লোকটাকে সহজ সরল পেয়ে কিরকম হেনস্তা করতেছে!😒 মুশফিক কি তোদের বাপ লাগে ! 😡😡,0,sports
সিলেট প্রতিটি বিপিএল এ কিছু চমক দেখায়,0,sports
ফকিন্নি যখন হঠাৎ করে ধনী হয়।,0,sports
আপনারা হয়তো এই কথাটা জানেন নাযে ক্রিকেটারা যে দফা আন্দোলন করেছে এটা একটা চালদেশের ভাবমূর্তি এখন অন্যা দিগে আছে। তাই এই চাল ব্যাবহার করা হয়তাই সবাই যেনো এটার প্রতি নজরদে ।আপনারা ভালো করে দাবি গুলো দেখবেনএখানে দফা আন্দোলন সরাসরি বিসিবির কাছে বলতে পারতো বিসিবি এগুলা মেনে নিতো না মানার কিছু নাই।,0,sports
অন্যকে পুটকি মেরে কিভাবে টাকা ইনকাম করা যায় তা তাহসিন নেশন কাছ থেকে শিখা যায়😂😂,0,sports
এমন অন্যায় মেনে নেয়া কষ্টকর 😭 😭,0,sports
আপনি আংকেল রাজনীতিবীদমাঠে রাজনীতি করেনক্রিকেটের কাচকলাও বুঝেন না অব্যহতি দেন দ্বায়িত্ব থেকে।,0,sports
বাংলাদেশ আর কোনো অলরাউন্ডার হবেনা সাকিব বাই বিশ্ব শেরা অলরাউন্ডার। 😂🤣,0,sports
আমার ম‌নে হয় ছে‌লেটা সত্য বল‌ছে!! ও‌রে হেনস্তা করাটা খুবই লজ্জার!! ক্রি‌কেট খেলার জন্য বাংলা‌দে‌শের যে টাকা খরচ হ‌চ্ছে এতে দে‌শে প্র‌তি বছর মানুষ দরিদ্র হ‌চ্ছে!!,0,sports
এটার অপেক্ষায় ছিলাম ভাইয়া,0,sports
অপেক্ষায় ছিলাম ভাই,0,sports
যাই হোক পরবর্তীতে দেখিয়ে দিব ইনশাআল্লাহ,0,sports
অবশেষে ভিডিও ❤❤অপেক্ষায় ছিলাম ধন্যবাদ।ভালোবাসা আপনার জন্য 💕💕💕,0,sports
কালো রুবেল হল একটি পাপি লোক একটি মেয়ের জিবন নষট করে দিল বিচার আমরা পাইনি কেন,0,sports
পাপনের দুই গালে জুতা মারেন,0,sports
ওকে আরেকটা সুযোগ দেয়া হলে ভালো হত।,0,sports
কি অবস্থা! ভাষা নাই থাকলেও এই চামচা গুলার জন্য তার প্রয়োগ করব না বাংলাদেশ এর কাহিনি ভাষা প্রয়োগের অযোগ্য!,0,sports
ইমরুল কায়েস কে শুধু শুধু বাদ দিচ্ছেন কেনো এইটা একটু বলবেন প্লিস।,0,sports
খুলনার কেকে আছেন লাইক দেন 🎉👍,0,sports
একজন উপরে উঠলে জনে লেজ টানে এটাই বাঙ্গালি,0,sports
সালাউদ্দিন সাহেব যেভাবে ফুটবলটাকে ধ্বংস করছে ঠিক একইভাবে আপন কাক্কু থুক্কু পাপন কাক্কু ক্রিকেট খেলাটা কে ধ্বংস করবে,0,sports
সময়ের মুল্য অনেক দাম আমি দিক্কার জানাই খেলা দুলাকে,0,sports
সাকিবের মুখটা মলিন 😥😥😥,0,sports
আইসিসির কোনো দোষ নেই সব দোষ পাপনের সব ভুল কথা বাংলাদেশ বড় চোর,0,sports
কে আগে নামাইলে ভালো হবে,0,sports
একটা সাকিব আল হাসান না থাকায় আমি সাকিব নামে পাগলটা খেলাও দেখি না এখন আর মিস ইউ বস্ 😢😢😢😢😢😢সাকিব আল হাসান 😢😢😢😢,0,sports
এই ইউটিওবার যে গরু চোর এতে কোনো সন্দেহ নেই তোর চোখে কি দেওয়ান বাগি মাজার পুজারি চেখে পড়েনা গরু চোরের মতো ওয়াজের পিছনে লাগছোত এসব বন্দ করো তুইতো মেহনত ছাড়া ইউটিওবে টাকা ইনকামের দান্দায় এসেছিস এটার কথা বলবে কে শুনি পাগল ছাগলের দল,0,sports
রুবেলের যায় গায় যদি আপনে হতেন তখন কি করতেন যারা রুবেল কে খালি দিতেছেন.......?????,0,sports
ভাই অনেক কষ্ট পেয়েছি সেদিন,0,sports
পাপনের পাচায় আঁচোলা বাঁশ দেয়া হোক,0,sports
সাকিবের অপরাদ সে প্রতিবাদি,0,sports
ভাই আমি ভারতে বাড়ি আমার তবুও আমি সাকিব কে খুব ভালো বাসি যদি পারেন শালা পাপন কে বাদ দেন সালাক বি সি সি আই লিডার মোহাম্মদ আশরাফুল কে লিডার করেন।,0,sports
সাবিকে সাথে আমরা আছি।,0,sports
অামার মতে বেতন অারো কমানোর উচিত খেলায় জিততে পারেনা অাবার মিসিল করে ওদের বাদ করে দেননতুন খেলোয়ার সংগ্রহ করেন,0,sports
আমি বুঝিনা পাপন সাহেব কি এমন ভুল কথা বলেছেন? যে কমেন্টে তার পদত্যাগ চান? এখন আমি পাপন সাহেব কাছে আরজি জানাই পাকিস্তানের প্লেয়ার কত টাকা পায় আর আমাদের প্লেয়াররা কত টাকা পায়? আর পাকিস্তান যদি চ্যামপিয়ন হতে পারেতাহলে আমাদের প্লেয়ার কাছে জেনে নিবেন,0,sports
ভালোবাসার এক নাম মোহাম্মদ সাঃ।যিনি বছরে একটি মিথ্যা কথা বলেননি।,0,sports
এটা নিশ্চয়ই পাপোনের চাল এটা বাংলাদেশ সরকার দেখা উচিত। বাংলাদেশের সম্পদ সাকিবুল হাসান,0,sports
পাগল আবোল তাবোল খবর সব কিছু,0,sports
সাকিব আল হাসান হারেনি হেরেছে বাংলাদেশ।,0,sports
যদি তাই হয় পাপন তুই আগে কি করে বললি সাকিব শাজাপাবে তরে আমি খাইয়া ফালামু,0,sports
হআপনি সত্যবাদী জধিষ্টির!!,0,sports
বাংলাদেশ অাওয়ামীলীগের চার বারের সফল সাধারণ সম্পাদকভাষা সৈনিকমুক্তিযোদ্ধা মরহুম রাস্ট্রপতি ও শহীদ অাইভী রহমানের সুযোগ্য সন্তান নাজমুল হাসান পাপন।ছোট বেলা থেকেই অত্যন্ত মেধাবী নাজমুল হাসান পাপন ঢাকা বিশ্ববিদ্যালয়ের অাইবিএ থেকে মাস্টার্স ডিগ্রি সম্পন্ন করেন। অামেরিকার ইউনিভার্সিটি অব ক্যালোর্ফোনিয়া এবং নর্থ ওয়েস্টার্ন ইউনিভার্সিটি সিকাগো থেকে এক্সিকিউটিভ এডুকেশন এন্ড মার্কেটিং স্ট্রেটেজি উপর ডিগ্রি লাভ করেন। সালে যোগদান করেন বেক্সিমকো ফার্মায়। তারপর থেকে নিজ যোগ্যতায় বাংলাদেশের ঔষধ শিল্পকে নিয়ে গেছেন এক অনন্য উচ্চতায়।দায়িত্ব পালন করছেন বাংলাদেশ ঔষধ শিল্প সমিতির সভাপতি হিসেবে। তার নেতৃত্বে বেক্সিমকো প্রথম বর্হিবিশ্বে বাংলাদেশে তৈরী ঔষধ রপ্তানি করে।সারা পৃথিবীতে তাকে স্বাস্থ্যসেবা ও ঔষধ নীতিমালা বিশেষজ্ঞ হিসেবে বিবেচনা করা হয়। লন্ডনের কমনওয়েলথ সচিবালয়ের একজন পরামর্শক তিনি।ঢাকা বিশ্ববিদ্যালয়ের অাইবিএর এলামনি এসোসিয়েশন সভাপতি।অসাধারণ ব্যবসায়িক নেতৃত্বেগুনের জন্য দুবাই এ অনুষ্ঠিত এশিয়ার সবচেয়ে প্রভাবশালী ব্যবসায়িক ব্যক্তিত্ব পুরুষ্কার এশিয়ান ব্র্যান্ড সামিট ঘোষিত হন নাজমুল হাসান পাপন। অামরিকার ম্যানেজম্যান্ট এসোসিয়েশন এবং অস্ট্রেলিয়ান ইন্সটিটিউট অব ম্যানেজম্যান্ট এর অাজীবন সদস্য তিনি। বহুমুখী প্রতিভার অধিকারী নাজমুল হাসান পাপন বিসিবির সভাপতি হওয়ার পূর্বে দায়িত্ব পালন করেন দেশের সবচেয়ে পুরানো ক্লাব অাবাহনীর সভাপতি হিসেবে। তিনি সভাপতি হওয়ার পর বিসিবিতে ফিরে অাসে সোনালী দিন।তার অার বহু পরিচয়ের মধ্যে অারেকটি বড় পরিচয় হল তিনি ভৈরবের মাটি ও মানুষের নেতা। ভৈরব থেকে বারবার নির্বাচিত সংসদ সদস্য। অাওয়ামীলীগ একটি অনুভূতির নাম সেই অনুভূতি হল সৈয়দ অশরাফ ও নাজমুল হাসান পাপনের মত ব্যক্তিরা। অাধুনিক ভৈরবের রূপকার হলেন নাজমুল হাসান পাপন ভাই। শত্রুমিত্র কেউ কোনদিন বলতে পারবে না পাপন ভাই কারু ক্ষতি করেছেন।ব্যক্তি জীবনে অতন্ত সফল ও পেশাদার এই মানুষটি বিসিবি সহ বহু প্রতিষ্ঠানের সভাপতির দায়িত্ব পালন করেন। যখন যে দায়িত্ব হাতে নিয়েছেন হয়ছেন সফল। যারা নাজমুল হাসান পাপন ভাই কে নিয়ে ঘোলা পানিতে মাছ শিকারের চেষ্টা করছেন তারা কোনদিন ও সফল হবেন না। রাজপথ ছাড়ি নাই পাপন ভাইয়ের ভয় নাইপাপন ভাই এগিয়ে চলো আমরা আছি তোমার সাথে,0,sports
এক কথায় বলতে গেলে এটা মানা যায় না । এটা কোন ধরনের বিচার । যেখানে সে সম্মানিত হবে অথচ সেখানে সে নিষিদ্ধ। এটা একটা চক্রান্ত ।,0,sports
সত্যি বলতে এতো কস্ট কেনো দিন লাগেনি আমার সাকিবের জন্য জতো টুকু কস্ট পেলাম বাংলাদেশ হারছে জিতছে কতো না কি ঘটেছিল তার পরে ও এতো কস্ট লাগে নি,0,sports
রাজশাহী সেরা এবার কাপ জিতবে ইনশাআল্লাহ। কে কে একমত???? লাইক দিন 👍👍👍👍👍👍,0,sports
কুমিল্লা ধন্যবাদ এমন বিজয় আমাদের কে উপহার করার জন্য। আর একটা অনুরোধ আমার একটা সপ্ন যে কবে পূরণ হবে যদি আপনারা একটু সাপোর্ট করেন তাহলে আমার সপ্ন টা পূর্ণ হয়ে যেত,0,sports
সাকিব ভাই আমরা এ রায় মানিনা,0,sports
পাপন কুকুর কে বাদদেক,0,sports
এই বিপিএল এর সবচেয়ে উত্তেজনাকর ম্যাচ ছিলো এটি কে কে একমত!একমত হলে লাইক দিন,0,sports
পিয়াজের সাথে মনে হয় তাদের ও দাম বাড়ছে ওদের বাদ দেয়া হউক নতুন দের সুযোগ দেয়া হউকলাখ টাকা বেতন আল্লাহর শুকরিয়া আদায় করা দরকার,0,sports
এই সমস্ত বান্দির পোলা দের জন্য খেলোয়াড়দের ইমেজ নষ্ট হয়,0,sports
তুমি তু প্রথম সারির নায়িকা না তুমাকে কয় জনে চিনে রুবেলকে বাংলাদেশ চাড়াও বাংলাদেশের সাথে যেই দেশ গুলো খেলে কমকরে হলেও ৫কোটি মানুষ চিনে যেমন ভারতে ১০০কোটি মানুষ আছে সবাই খেলা ভালবাসে ভারতের ১০০কোটি মানুষের মধে্ৌ করে হলে ও ২০ কোটি মানুষ খেলাটি বোজে তেমনি আরো অনেক দেশ যেই গুলো উদহারন নাই দিলাম,0,sports
খুব খারাপ লাগে যত দিন সাকিব আল হাসান না আসবে ক্রিকেট খেলা দেখব না,0,sports
যে খেলাটাকে আমি আমার চেয়েও ভালোবাসিআজ সেই খেলা থেকে নির্বাসিত হওয়ায় আমি দুঃখিত।আমি সব দোষ স্বীকার করে নিচ্ছি।; 😌 সাকিব আল হাসান।,0,sports
ভালো লাগে,0,sports
সালা একটা পালতু,0,sports
বিসিবির সবাই আঙ্গুল ফুলে কলাগাছ হয়েছেকিন্তু খেলোয়াড়রা অসুস্থ হলে সরকার বা বিসিবির কাছে এখনো হাত পাততে হয়কেন?????,0,sports
বাংলাদেশে একটার পর একটা ঘটনা ঘটতে থাকে।।।তবে সাকিবের এই ঘটনা আমাকে অনেক দুংখ দিয়েছে,0,sports
তুইকি পাগল,0,sports
বিসিবি এতো দিন পরে কেমন করে জানলো,0,sports
বেড সাব্বির ব্যায়,0,sports
দেশ কে যে ভালোবাসবেদেশের কুলাঙ্গার রা তাকে চুদে দিবে,0,sports
আজকে দেশী নতুন রা ভালো খেলছে,0,sports
শালারা নাচতে পাড়ো খেলার মাঠে গিয়ে ডিম মাড়ো কেন।,0,sports
আপনার কথা রাইট,0,sports
বাজে কথা,0,sports
সালা,0,sports
ব্যাড বয় <br />আমার প্রিয় প্লেয়ারের একজন।,0,sports
"সৌম্য, লিটন ফর্মে নাই, তা নিয়ে আমাদের মাথাব্যথা নাই, যত দোষ নন্দঘোষ, আমাদের সমস্যাটাই এখানে, আমরা সাব্বিরকে উৎসাহ না দিয়ে নিন্দা করছি। এমন করলে আমাদের ক্রিকেট সামনে যাবে কিভাবে?",0,sports
মালান অসাধারণ খেলেছে,0,sports
যতদিন সাকিব নাই থতদিন খেলা দেখবোনা,0,sports
অামি নিজেও এক জন বাংগালী তবুও কই তে চাই লোকে জে বলে খামোখা বলে না! মুরখো চুদা বাংগালী হিংসা দিয়া ভরা! এটা করে নিজেদের খতি করলি রে! পাপন দপশ বিরোধী কাজ করছে! এই পাপন খানকে র পোলায় কেন পদত্যাগ করে না! খমতার বরাই কত কাল করবি মুর্খ,0,sports
পাপনের পদত্যাগ চাই।,0,sports
কুমিল্লার হাইলেটস টায় এত কম কেন রংপুর মিনিট আর কুমিল্লার মিনিট তুই কি রংপুর এর দালাল নাকি?,0,sports
পাপন ভাই টাকা কিন্তু জনগনেরকেওর বাপের টাকা ওদেরদল থেকে বাদ দেওয়া হউক,0,sports
সাকিব যদি না খেলে তাহলে এ জাতীয় খেলাটাও ধংস হয়ে জাবে প্রধানমন্ত্রী শেখ হাসিনা র কারনে বাংলাদেশের আজ এই অবস্থা ধংসের পথে,0,sports
জুতা মারি পাপনের কপাল,0,sports
রুশোর দুই বলে দুইটা ছক্কার মধ্যে একটা দেখাইছে আর ক্যাপশনে অল বাউন্ডারি মারে!🐸 বাল🙄,0,sports
দু চোখের কান্না ধরে রাখতে পারছি না।আর কোনদিন খেলা দেখবো না।এদেশে সত্য কথা বলা যাবে না।,0,sports
খুলনা চাইলে আজকের ম্যাচটি জিত্তে পারত।আবালের দল শিরোপা হাতের কাছে পেয়েও হাত ছাড়া করছে। বলে রান দরকার ছিল।হাতে ছিল উইকেট। ব্যাটিং এ ছিল মুশি আর ফ্রাঙ্কলিন। কিছু করার নাই।ভাগ্য যে কখন বদলে যায় তা কেউ বলতে পারে না।চট্রগ্রামের পরে খুলনার সাপোর্টারস হয়েছিলাম।কিন্তু এদেরও দেখি বাশ দিয়ে ছেড়ে দিছে।অভিনন্দন রাজশাহী,0,sports
হাসতে হাসতে পেট ব্যাথা হয়ে গেছে ৷,0,sports
ভালো লাগে মুশফিক ভাইকে,0,sports
যে মানুষ আনন্দ দিয়ে চলে জাই তার জন্য কৃষট হয়,0,sports
ভালোই খেলা হয়ছে,0,sports
পাপন মুক্ত বিসিবি চাই ও পদত্যাগ চাই,0,sports
লঘু পাপে গুরু দন্ড । কু সন্তান পাপন ব্যাপার টা জানতো তাহলে একজনের শাস্তি হবে কেন? পাপনেরও শাস্তি চাই ।,0,sports
ভাই পাপন যে কোন কিছুর মূল্যে পাপন গদি চায় দেশের ভালো চায়না দেশ জাহান্নামে,0,sports
রুবেল হোসেনের পায়ের কাছে যাবারও তোর দক্ষতা নেই,0,sports
পর্যায়ক্রমে লাখ টাকা পর্যন্ত আমাকে ঘুষের অফার করলো এক লোককিন্তু আমার চাহিদা আর ও বেশী ছিলো তাই প্রত্যাখ্যান করেছিলাম।পুলিশ ঘুষের খবর জানার পর আমাকে ধরে নিয়ে গেলো।আমি পুলিশ কে বললাম স্যার আমি তো ঘুষ খাই নাইআমি তাকে ফিরিয়ে দিয়েছি ☺ স্যার আমাকে ছেড়ে দিন 😎 আশ পাশের কিছু বাঙালী এ কথা শুনেই বললো উনি ষড়যন্ত্রের স্বীকারকিছুদিন আগে ওর অফিসের বসের সাথে ঝামেলা হইছিলো তাই উনার বস উনাকে ফাসানোর জন্য এসব করেছে 😂😂সুত্রঃ দৈনিক বালের কন্ঠ।,0,sports
সবগুলা কথাই ঠিক,0,sports
সাব্বিরকে তখনও ভালোবেসেছি আর একনও ভালোবাসবো,0,sports
তারমানে জুয়াড়ি সাথে ওদের হাত আছে শাকিব জানত এদের কথা বললেও ওরা কিছু করতে পারবে না তাই বোর্ডকে জানায় নাই,0,sports
সময় টিভিকে বলব<br />আপনারা একজন ব্যক্তিকে নিয়ে নিউজ করেছেন ভাল কথা<br />কিন্তু তার ব্যক্তিগত মোবাইল নাম্বার কেন দিলেন,0,sports
বিশ্ব সেরা আলরাউন্ডার আপমান করলো খুব কষ্ট পাইলাম।।।।,0,sports
হ্যাপি আসলেই অনেক ভালো একটা মেয়ে।,0,sports
আগারওয়াল,0,sports
সাকিবের কথায় প্রমাণিত ভারতের বিপক্ষে জেতা ম্যাচ কেন হারে বাংলাদেশ! এতদিন খেলা দেখে শুধু মনে হতআর এখন সেটা প্রমাণিত!,0,sports
যারা গালি দিয়ে ফেলেছেন তারাপ্লিজ লাইন থেকে সরে যান। পেছনে এখনো অনেক মানুষ লাইনে দাঁড়িয়ে আছে । সবাইকে গালি দেওয়ার সুযোগ করে দিন। কেউ বিশৃংখলা করবেন না ।,0,sports
এখন সব খেলোয়াড়ের উচিৎ সাকিব ভাইয়ের পাশে দাড়ানো আর খেলাকে বর্জন করা।,0,sports
ক্রিকেট প্রেমী রা পর্যন্ত এই ম্যাচ ফিক্সিংয়ের প্রস্তাব কথা অনেক দিন আগে জানে। এবং সেটা পাপন কে জানিয়েছিল ।আজ পাপন বলেছেন সে কিছুই জানে না !!!!,0,sports
ইমরুল কে বিসিবি নিয়মিত দলে নিতে চায় না। অথচ সে ভালো‌ খেলে,0,sports
এটা হলো সরকারের নিল নকসা এতোদিন কেনো এটা প্রকাস পেলোনা পাপন তুমি একটা পাপি ছি ছি ছি পাপন দেশের ফোন রেকর্ড কি ভাবে পেলো ওরা,0,sports
"নারী, আর টাকার প্রতি যাদের লোভ,তারা ধ্বংস প্রাপ্ত হবেই, যেমন, নাসির ,সাব্বির, এরা এখন খেলার মধ্যেই নাই,এরা ক্রিকেটের প্রতি সৎ ছিল না,তাই তাদের এঐ পরিণতি???দুঃখ জনক, অনেকে সুযোগ পায় না ,আর অনেকে পেয়েও হারায়???",0,sports
নাসির লুচচা তাই মানুষ বলছে,0,sports
আপনাদের সময় সংবাদ চ্যানেলের যে কোনো সংলাপের সময় দেখি সাউনড কম হয়। একটু বারিয়ে দেবেন,0,sports
কোয়াব টাকার খোয়াব দেখে।,0,sports
তামিম ইক বাল এর চেয়ে রনি তালুকদার অন্নেক ভালো ব্যাটসম্যান,0,sports
অভিনন্দন সাব্বির রহমান,0,sports
আপনার কথা শুনে সত্যি ভালো লাগলো,0,sports
শালা কি বলে,0,sports
তুই যে পাগল তর কি কোনো কনফিউশান আছে আমার নাই।,0,sports
শালা তুই এই ক্রিকেট খাইছিস,0,sports
রুবেল জদি জাতীয় দলের খেলোয়ার না হতো ওকে জুতা পিটা করতো মিডিয়ার আটিস্ট রা,0,sports
লুইচ্ছা,0,sports
সাকিব ভাই হেরে গেলো,0,sports
সৌম্য ভাইকে ক কে পছন্দ করেন তারাই লাইক দিন,0,sports
এ কেমন মজা খুব খারাপ,0,sports
কি খারাপ মুখরে তো,0,sports
ও গালি কেন দিবে! ওরে অধিকার কে দিছে। আর যারা ওরে সাপোর্ট দিচ্ছে তারা অরজিনাল শুয়োর আর ওরা যেন আজ থেকে বাংলাদেশ এর খেলা না দেখে!,0,sports
মুসি লাভ ইউ বস আমার সবচেয়ে পছন্দের প্লেয়ার,0,sports
গাজা খুরি ভিডিও,0,sports
পাপনদা কে ইন্ডায়া পাঠান,0,sports
সামান্য বিষয় নিয়ে এতকিছু কেন,0,sports
দাড়ি বিষয়ে কথা হচ্ছেনা কেন?,0,sports
তম দাবি পাপনের পদত্যগ,0,sports
ক্রিকেট খেলায় যতই বড় মাপের খেলোয়াড় হোক না কেনোসবাইই সাকিবের মতো ফিক্সার। তাই এসব সাকিব দের জন্য এত আবেগ দেখায় লাভ নাইবুজসো? সবাই টাকার জন্যই খেলে। দেশ হাজারো সমস্যায় জর্জরিতসেগুলো নিয়ে ভাবুন। ভাইরাল করুন সেগুলো। শাক দিয়া যাতে মাছ ঢাকার চেষ্টা না হয়।,0,sports
সবাই ভালো আছেন?? যারা করছেন তাদেরকে বলছি 😍,0,sports
শুরু থেকেই বলছি রাজশাহী ইনশাল্লাহ ক্যাপ নিবে এখনো বলছি ওস্তাদের মার শেষ রাতে কে কে মানেন লাইক দিন👆🖐🖐🖐🖐👍👍👍👍👌👌,0,sports
বাংলাদেশ দল কতো কোটি টাকা লাভ করে দেসে এনেছে জে তাদেরকে গাজা খাওয়ার জন্য আবার দাবি মানতে হবে আমরা হচ্ছি ছাগল জাতি কারন বাংলাদেশ জখন বিশ্ব কাপ খেলে তখন আপগানিসতানের খেলোয়াররা তখন হাপ পেন পরে ঘোরে তারাই আজ বাংলাদেশকে হারায় আহা কি সুন্দর,0,sports
তাসকিন কে খুব ভালো মনে করতাম,0,sports
শুভ কামনা রইলো বসের জন্য,0,sports
খেলা বন্ধ করে দেওয়া উচিত কারণ মানুষের সময় অনেক নষ্ট হয়আর মানুষের অনেক সমস্যা হয় ।,0,sports
ভাই সত্যি কথা বললে এমন হয়,0,sports
ভাই এগুলো শুনতে আর ভালো লাগে না!!! খুব কষ্ট লাগে,0,sports
বাংলাদেশের অর্ধেক সুবিধা এরা পায়আর কি চায় ওরা!! জনগণের সব টাকা ওদের হুগাদিয়া ডুকায়া দিক!!খেলার সময় বালের মাথা!! ওদের যে সুযোগ সুবিধা দেওয়া হচ্ছেবাংলাদেশের ম শ্রেণীর সুযোগ সুবিধা দেওয়া হচ্ছে!! সবগুলার শরীরের তেল জমছে,0,sports
কথা বলার সময় থেমে যান ক্যান ভাই???হাওয়া শেষ হইয়া যায় নাকি বলতে বলতে??,0,sports
প্লেয়ার দের টাকা বারাতে গেলে খুব খারাপ লাগে আপনি পিছন দিয়া কত টাকা মারেন তা কি জাতি জানে।কয়দিন আগেও তো আপনার ক্যাসিনোতে ছবি ভাইরাল হইছিলো। টাকা পান কই আপনার বেতন কত।,0,sports
ছাব্বির একটা ভাল ছেলে,0,sports
সাকিবের সাযা যাতে কমানো যায় সেদিকে খেয়াল রাখা উচিত।,0,sports
উচিৎ কথা বলছে এখন গায়ে লাগছে।পাপন আপনি পদত্যাগ করুন,0,sports
মুশফিক ভাইকে জিজ্ঞেস করা হইছিলো কি যে গালি দিয়েছে কিনা,0,sports
তার জন্য ফোন number টা এভাবে দেখানো ঠিক হয় নাই।,0,sports
টিম ম্যানেজমেন্ট নিজেরাই জানে না কোন খেলোয়াড়দের কোথায় খেলাতে হবে। আর দোষ হয় সাকিব রিয়াদদের।,0,sports
খেলা পারেনা আবার বেতন বৃদ্ধি চুদায়,0,sports
প্রথম ভিউয়ার আমি,0,sports
টি টোয়েন্টি হাইলাইটস ম্যাচ মিনিট কিভাবে হয় আমার বুঝে আসে নাহ,0,sports
রুবেল ভাই গুড,0,sports
ফিংগার স্পিনার আর রিস্ট স্পিনার এর পার্থক্য আগে জানা উচিৎ পাপন সাহেবের,0,sports
আপনার বন্দুতো জুয়া খেলে,0,sports
অ্যাম্পিয়ার গাজা খোর,0,sports
ডমেস্টিকের পাইপ লাইন ঠিক করেন জাতীয় লীগের পিচ্ গুলো ঠিক করেন নতুন নতুন খেলোয়াড় তৈরীর ব্যবস্থা করেন।,0,sports
আহারে 😭😭😭😭,0,sports
খুলনার সাপোর্ট কে কে???,0,sports
আমিরের ভক্ত গুলা কুতাই আমি দেকতে চাই,0,sports
তিন দিনের বাসি পানতা খাইছেন নাকি।আপনারে কেডাই কইল সাকিব ইংলান্ড এ খেলব😂😂,0,sports
সাকিবের জন্য প্রতি জেলায় জেলায় আন্দোলন চলবে 🙋🙋🙋🙋,0,sports
সাকিব কোটি কোটি টাকার মালিক কোনো সমস্যা নাইআমরা গরিব টাকা নাইকোনো রকম খাইয়া দিন কাটাই,0,sports
আমি পাপনের পদত্যাগ চাই,0,sports
এই বেয়াদবটাকে কেনো নেওয়া হয়।আর তার জন্য জাতীয় দলের বদনাম হচ্ছে।,0,sports
ভালোবাসি সাকিবকে ফিরেএশো ওতি তারা তারি,0,sports
মিসস করি সাকিবআল হাসান কে,0,sports
গ্যালারি যাবে,0,sports
মুশফিক একটা হাফ সেঞ্চুরি করে আঙ্গুল দিয়ে ফ্লিল্ডার গনা শুরু করেছে একবার নয় কয়েকবার ভাবছি রোহিত শর্মার মত যদি কখনো ব্যাটিং করে ফেলে তখন কি করবে এরা ?,0,sports
এই প্রথম তাহসিনেশন এর কোনো ভিডিওতে লাইক দিলাম সাবস্ক্রাইব করলাম।ধন্যবাদ তাহসিন।,0,sports
এত কিছুর পরেও কি আপনাদেরকে সব কিছু বলতে হবে। বুজতেই পারছে বাংলাদেশ ক্রিকেট বোর্ড সাকিব যে কতটা গুরুত্বপূর্ণ।,0,sports
হিন্দি গান দিয়ে নাচানাচি করে আবার হিন্দি ফিল্ম দেখতে গেলে অবরোধ চালু করে শিল্প সমিতি বলে হিন্দি ইন্ডিয়ান সিরিয়াল বাদ দিতে হবে মাগির পোলা জাতীয় দলের ওরা । পারেনা খেলতে। ক্রিকেট পক পক করে নাচে।,0,sports
আমাদের জন্য খুব খারাপ খবর সেইটা হল তোর মাকে জনে চোদে চে,0,sports
অ্যামেজিং পারর্ফমেন্স,0,sports
প্লিজ ভাইয়া আমার চ্যানেলটা সাবস্ক্রাইব করুন সাবস্ক্রাইব করে একটা লাইক দিন এবং একটা কমেন্ট করুন আশা করি পাশে পাবেন এবং আমি আপনার চ্যানেল সাবস্ক্রাইব করব ইনশাল্লাহ ??,0,sports
সব ক্রিকেটারদের ধন্যবাদ পাপনের মুখোশ খুলে দেওয়ার জন্য যত তাড়াতাড়ি পাপনের পদত্যাগ চাই ভালো একজন মানুষকে দায়িত্ব দেয়া হোক,0,sports
বালের সিলেট ফকিন্নি মার্কা টিম,0,sports
যদি এরকম ব্যপার হয় তাহলে তো সাকিব আল হাসানের কোন অপরাধ নেই। এটা তাঁর বিরুদ্ধে চক্রান্ত। সাকিব আল হাসানের উচিত আর কোনদিন জাতীয় দলে না খেলা। বোর্ড কর্তারা খেলুক।,0,sports
পাপন ও শেখ হাসিনার কারসাজি এই নাটকের মূল ভিলেন শেখ হাসিনা আর সাইড ভিলেন পাপনতাদের সেই দিনের গোপন বৈঠকশাকিবকে ফাসিয়েছে। এটা সুস্পট।,0,sports
ব্রো জিন্দাবাদ 😂😂😂,0,sports
তুই আগে বাহির হ।,0,sports
আরেক টি কথা সাকিব সাথে জারা তাল মিলিয়েছে তাদের কি হবে তারা যুদি এক না হতো তাহলে সাকিব একা কি করতে পারতো আমি সকলের পতি অনুরুদ করি জারা এক সাথে আন্দলন করেছেন আজ আপনেরা কেন কথা বলেন না সকল খেলোয়াড় দের বলছি আপনেরা সকলে এক হয়ে যান,0,sports
আমরাআবারচাই শাকিব কে মাটে,0,sports
এতদিন কোথায় ছিল এই নিষেধাজ্ঞার খবর?যেই নিজেদের স্বার্থে টান পড়ছে তখন সাকিব এই করছে ওই করছে।আমরা আম জনতা এখন সব বুঝি। যে কতবড় চতুর তা এখন সবার কাছে পরিষ্কার। কি এতদিন বাল ছিড়ছিল?পারলে একটি সাকিব বানায়ে দেখাক ।সাকিব সাকিব ই।বিশ্বের সকল বোর্ড দের সাথে থাকে সবসমই আর আজ কি দেখালো আমাদের।হায়রে,0,sports
কে বলে আমার দেশি পারে না। তো বলছে ভালোবাসা অবিরাম ভাই ফিজ,0,sports
তোর তো বাল ও উঠেনাই,0,sports
সালাম পাপন সালা ভারত থেকে ভাল পলিটিকস সিখেছ আজকে একটা হাদিছ সুনলাম আল্লাহতায়ালা কিছু বান্দার বিচার দুনিয়ারটা দুিনয়ায় করে তাই সালা অপেক্ষাকর এর ফল পাবি তোর মাকে মারল এত কস্ট দিয়ে(যার সাস্তি এখন একজন বিদশ ও জেলে আছে ) বাপও নাই তারপরও কি মরার ভয় ও তোদের শিক্ষা হবেনা । আওয়ামীলিগকে ভাল ভাশি তোদেরনা প্রধানমনত্রির সাংবাদিক সংম্মেলন দেখলাম ক্লাব জুয়ারিদের কথাবল্লেন খেলাত শুরুহয়েছে কয়েক বছর পূর্বেই তখন সাংবাদিকরা কলম চুসছে কারন যে আইন করেছেন লিখলেইত কেইছ হয়ে জাবে কিছু পেপার বা মিডিয়া লিখে ব্যাবসা করারজন্য আরলিখলেই কি হবে বিচার করবে কে? বিতরকৃত যে হত্যাকান্ড শেয়ার বাজার লোট আপনি দেশকে যে উন্নতির টাকা দিচ্ছেন তাত বালিস আর বই নাছিম সাহেবর হাসপাতল দিনের রাস্তাআরও কতকি আসেপাসের লোকেরাই খেয়েফেলছে মাসে কয়টা দূরনিতিবাজ ধরেছে ও কেইছ ও বিচার হয়েছে দুদুক তনা যেন দূরভুক বাচ্চো সাহেবের কোন কিছুই পায়নায় আর আপনার সরকারি লোক ধরতে পৃর্ব অনুমতি লাগবে যা এক দেশে আইন তা এখন কার বিচার হবে ?তাই যে বলবে লিখবে সেত সাগর রুনিআবির সাকিবের মত বলির পাঠা হবে আমিও হতে পারি তাই আপনি লিখতে বলেছিলেন লিখলাম তাই চাওয়া ও দেওয়ার মালিক আল্লাহ তাই তার কাছেই চাইলাম বিচার ও এইদেশের মানুশষের সুন্দর জীবন সাকিবের সুন্দর জীবন কামনা করি আর এই ক্রিকেট এই দেশে না খেলতে জতদিন এই পাপন গংরা আছে এ শেখ মুজিবকে মারার পর আব্বা আমাকে বলেছিল যে দেশে ফুলের বাগানের মালিকে মেরে ফেলে তবে বাগানের ফুলচাস বা বাগানই বা সুন্কদর করবে কে তাই এই দিশে আর কোন নেতা তৈয়ার হবেনা হয়েছেও তাই এখন কই আমাদের নেতা জিয়াখালেদাতারেক এরসাদজামাত ও তার সারগিতরা ? পলটনে রিজবি চেনেলে রাত্র কালিন টা সংবাদ পাঠ করলে বিরধী দলের কার্যক্রম হয়না আর আন্দালিব আছিফ নজুরুল ছার ব্রি: শাখওয়াত সাঃআনিছুল হক আর অনেকে (ছাগল রনিকে ছারা )কত বলছে ও লিখছে কৈ কিছু হচ্ছে ? তবে মানুশের অন্তরে যে রক্ত ক্ষরন তা যখন হবে তখন কিন্ত পৃথিবার কোন হাসপাতলে এই নিতিহীন দূরনিতিবাজদের চিকিৎসা দিয়ে বাচান জাবেনা তাই এখন হাছিনা আপার দিকে আমরা জিরু টলারেনসের নজর রাখছি ওনার কর্মের ফল কি হয় সুশাচ্ছথ কামনা করছি আসুন আমরা সবাই সত্যকথাসৎকর্ম সৎবিচারও ভোটের সময় টুপি তজবি হাদিছফতুয়া তাহাজ্জদ পরে না বলা হজের মর্জাদা রাখা আর বিদেশে আমার ভাই বোনরা রক্তে করা উপার্জনের টাকা লুপাট না করা দেশের মানুশদের রেখে বিদেসিদের জন্য আবেগ মানবতা না দেখান কোন ধর্মিয় নামে সংজ্ঞঠন রাজনিতি মাজার পুজারি ইসলামের বিরুদ্দাচার না করা ইলেকট্রিক মিডিয়ায় ও ছবি সহ রেজিস্ট্রি করা সকল মোবাইল সিম পূনরায় ও ছবি সহ হালনাগাদ করা পূর্বেই নাম্বার এলাকা ভিত্তিক করে দেওয়া এবং এর মাধ্যমে বিক্রির করা ও দেশকে ভাল ভাশি,0,sports
সাকিব আমরা চাই,0,sports
আমি জানি কেন সাকিব কে জানায় নি।আগারওয়াল ছিলো দের লোক। সাকিব খেলার সময় তাকে ওই মাফিয়ার লোকেরা ফিক্সিং এর জন্য প্রস্তাব দেয়।আর থ্রেড দেওয়া হয় যাতে কে না জানায়।এরা খুবই ক্ষমতাবান ভারতীয় মাফিয়া।এদের কাছে বোমা ।সাকিব কে জানিয়ে নিজেকে এতো বড় রিস্কে ফেলতে চায়নি।তাই জানান নাই।আর সাকিব পাপনের বিরুদ্ধে আন্দোলন করায় পাপন সাকিবের বিরোধীতা করছে।অর পাপনতো এখন কেসিনোতে জুয়া খেলায় মশগুল।আল্লাহ বিচার করবে নয়তো জনগণ,0,sports
পাপনের চাল কি বলেন আপনারা,0,sports
জোস ভাই। হাই লেভেল এর জুয়ারি হালায়।পা পোন্দা😂,0,sports
পাপন রে পদত্যাগ করিয়ে দাও,0,sports
চিটাগাং জিতলে ভালো হত ফাইনাল ম্যাচ হত জমজমাট,0,sports
বস আমরা আছি তোমার সাথে,0,sports
দল থেকে আজীবন বহিষ্কার করা হউক।,0,sports
এক দিন যে ভাল খেলে তারে নিয়েই নাচানাচি করে আবার জিরো বানিয়ে দেয়,0,sports
আরে ভাই এটা তার ভালবাসার,0,sports
যে পযর্ন্ত শাকিব ভাই খেলবে না সেই পযর্ন্ত আমি আর খেলা দেখবো না ভাইয়া রা।,0,sports
ক্রিকেটে আর টাকা না ঢেলে সরকারের উচিত ফুটবলে সুনজর দেয়া 🙂,0,sports
ভাই এইভাবে বসে বসে জাতীয় সংগীতের মিউজিক দিবেন না প্লিজ,0,sports
ভালের নিউজ,0,sports
এতে বিপদ হয়,0,sports
গালি দিচে তো কি হয়েচে বাল চাল কেনো দালালি করে,0,sports
সাকিবের চেয়ে কি বাংলাদেশের ক্রিকেটের জন্য পাপন বেশী জরুরী। 😡 মাশরাফি এম পি র ক্ষমতা নিয়ে মাননীয় প্রধানমন্ত্রী কে পাপনের কুকীর্তীর কথা বলুন। যদি সত্যিকারের খেলোয়ার হয়ে থাকেন।,0,sports
আমার ভুল হলে ক্ষমা করবেন,0,sports
ভাইয়া বাংলাদেশের দালালরা যে মেয়েদেরকে বিদেশে পাঠায় এইসব নিয়ে কিছু করেন,0,sports
সবাই কি অাবাল নাকি দুষ্টু গরুর চাইতে শূন্য গোয়াল ভাল। সাকিব অতি অহংকারী।তার যে অান্দোলন সেটিতেও একমত না অাবেগ দিয়ে জিবন চলে না। সাকিব এর চাইতে বড় বড় ক্রিকরটারা ক্রিকেটে নাই তাই বলে কি ক্রিকেট ধ্বংস হয়ে গেছে নাকি।,0,sports
ক্রিকেটারদের আন্দোলনে নেতৃত্ব দেওয়ার কারণে ও শেষ পর্যন্ত অপরাজনীতির শিকার হলেন। শিক্ষণীয় : অন্যায়অনিয়মদুর্নীতির যে সিস্টেম সমাজের সকল স্তরে দীর্ঘদিন ধরে চালু আছেসেই সিস্টেমের বিরুদ্ধে সাহস নিয়ে কথা বললে আপনাকেও নির্যাতনপ্রহসনের শিকার হতেই হবে।আর তাতে আপনি যেই হোন না কেন!! বাংলাদেশের জানসাকিব আল হাসান!সাকিব আল হাসান একটা ম্যাচে ভালো না খেললে যেই ক্রিকেট পাগল জাতি এখনও একটা ম্যাচ ঠিক মতো জিততে পারে নাসেই দেশে সাকিবকে শুধু শুধু রাজনৈতিক কারণে নিষিদ্ধ করার তীব্র নিন্দা এবং প্রতিবাদ জানাচ্ছি।যদিও বিসিবি অন্য কারণ দেখাচ্ছে।তবে এগুলো অজুহাত ছাড়া ভিন্ন কিছুই নয়! অক্রিকেটিয় একজন লোক একজন রাজনীতিবিদ এমপি পাপন সাহেবকে কেন বিসিবির সভাপতি বানাতে হবে?কেন সাবেক কোনো ক্রিকেটারকে বিসিবি বস বানানো হচ্ছে না? ক্রিকেট বোর্ড চালাতে হবে ক্রিকেট জগতের লোক দিয়েরাজনীতিবিদ দিয়ে না। পরিশেষেনাজমুল ইসলাম পাপন সাহেব এদেশের ক্রিকেটে কিছু দিতে পারেন নি।ক্রিকেটের উন্নয়নে তার কোনো অবদান নেই।আজ বাংলাদেশের ক্রিকেট যে অবস্থানে পৌছেছেসেটা সাকিব তামিমদের হাত ধরে পৌছেছে।সাকিবের মতো প্লেয়ার বাংলাদেশে অতীতে কেউ আসে নি ভবিষ্যতে আরও বছরে কেউ আসবে কিনা সেটাও সন্দেহ।বাংলাদেশের একমাত্র আন্তর্জাতিক মানের প্লেয়ার সাকিব আল হাসান।যে পৃথিবীর সকল টিমে জাতীয় দলে খেলার যোগ্যতা রাখে।তাই তাকে নিয়ে আর রাজনীতি না করে তাকে মাঠে ফেরানোর ব্যবস্থা করুন।সাকিব ছাড়া বাংলাদেশ ক্রিকেট কল্পনাও করা যায় নাতবে ব্যক্তিস্বার্থ চিন্তা করলে সাকিব চাইলে অন্য যে কোনো দেশের নাগরিকত্ব নিয়ে সেই দেশের জাতীয় দলে খেলতে পারে।তাই এমন ভুল আর কইরেন না পাপন সাহেব।এককথায় সাকিব ক্রিকেট বাংলাদেশ একই সূত্রে গাঁথা!,0,sports
"ভালো খেললেও তোদের ভরে না,,।<br />শালার পুতে রা,,।<br />যে মাটিতে কেও দারাতে পারে নাই সেখানে বস 100 মেরে দিল,,।<br />তোরা সমালচোনা করস কেন,,।",0,sports
এখন বুঝতে পারবে যে সাকিব কি জীনিস ।আর হে এখন পাপন খেলবে।,0,sports
এটা কোন বাপার না সব মিথ্যা আমি সাব্বির কে ঘৃনা করতাম এখন ভালবাসি ও কে খেলতে দিন জাতীয় দলে ওভাল হবে,0,sports
উল্টাপাল্টা খেলবে গালি দিবেনা ভালবাসবে আমাদের ট্যাক্সের টাকা খাবা আর খারাপ খেলবা গালি দিবে না আদর করবে চামচাদের মধ্যে যে মুশফিকের গেন্জি পরেছে ওর কথাবার্তাতো মুর্খের মত আর পুরা ইয়াবাখোর লাগছে।,0,sports
রাসেলের জাদুর ব্যাটিং এ আমরা ফাইনালে। 🤭🤭👌👌👍👍👍👍💓❤❤💓💓,0,sports
সাকিবের প্রতি আমি দুঃখ প্রকাশ করছি ছোট্ট ভুলের বড় মাসুল,0,sports
পিছনে মদদী এটা কেমন করে দেখ সবাই। তুই যে রাস্তার ছেলে চেহেরা দেখেতো বুঝা যায়,0,sports
পাপনকে ভাগাতে হবে।,0,sports
পাপন তুই জিতে গেছো,0,sports
বাবা চালিয়া যা,0,sports
বাহ চমেৎকার। সিলেট খুলনাকে হারাই দিলো 😂,0,sports
ধনের বাল খেলছো আবার নাটক চুদাও,0,sports
"বানচোদের বাচ্চার ছবিটা দেখলে বুঝা যায় ,শালা লুচ্চা,",0,sports
আসসালামুআলাইকুম আমার চ্যানেলটা সাবস্ক্রাইব করার জন্য বিনীত অনুরোধ করছি সবাইকে সম্ভব হলে পরিচিত সবাইকে বলবেন যেন সাবস্ক্রাইব করে । সবাইকে ধন্যবাদ,0,sports
শুনেছি আল্লাহ পাক তাকে এ পথ থেকে ফিরিয়ে এনেছে সত্য কিনা জানিনা,0,sports
শাকিব আল হাসান কে চাই,0,sports
এই গুলা সবাই মিলে একটা ক্যাসিনো,0,sports
এখন কি করা যায়,0,sports
পাপনের পদত্যাগ দাবী করছি,0,sports
ধন্যবাদ নাহিদ ভাই।এই মূহুর্তে আপনার উপস্থাপনা অনেক প্রয়োজন সূলভ।তা আমরা পেয়েছি। আপনার জন্য দোয়া ও শুভ কামনা করি। আগামীতে আপনি আরো কিছু সত্য বিষয় নিয়ে সঠিক উপস্থাপনা করবেন।,0,sports
পাপন ও নান্নুকে বহিষ্কার করা হোক।,0,sports
মুশফিকুর রহিম একজন ভাল ব্যাটসম্যান।,0,sports
খুলনার ভক্ত থাকলে লাইক দাও,0,sports
আমি শুধু এটুকুই বলবো বাংলাদেশের এর জন্য একে একে এগিয়ে নয় পিছিয়ে যাচ্ছে!!!!!!!!!!!!,0,sports
আরে ভাই সমস্যা কি পাপন আছে সে এখন ব্যাট হাতে মাঠে নামবেন। কিছু বললেতো আবার কমেন্টকারিকেও হয়ত বের করে সাজা দিবে তাই শুধু একটা কথা বলে রাগ ঝাড়ি পাপন সালালালা নিজে এখন মাঠে নেমে খেল দেখব তোর কত দম,0,sports
তাকে নিয়ে লাগলা কেন আবার,0,sports
ভাই আপনার কথা শুনে কান্না চলে আসলো।,0,sports
সাবাশ রুবেল।।,0,sports
ফকিরের টাকা হলে যা হয় আরকি,0,sports
পাপন কে পদত্যাগ চাই,0,sports
হইছেতো এখন ছাইড়া দেন ওকে ভাইরাল করার কি দরকার,0,sports
ঢাকার ভক্তরা কমেন্ট করুন খুলনার ভক্তরা লাইক দিন,0,sports
সৌম্য ও তাসকিনকে দলের সিলেক্টর ও ম্যানেজার বানিয়ে দিলেই তো ল্যাঠা চুকে গেল। সৌম্য ও তাসকিনকে আর চান্স দিতে হবে না। দলে একেবারে পাকা স্থান হয়ে যাবে।,0,sports
ধন্যবাদ ভাইয়া আপনাকে সুন্দর এবং নৈতিক বাচক কথা বলার জন্য হুম আমরা সাকিব ভাইয়ের পাশে আছি থাকবো ইনশাআল্লাহ,0,sports
খেলতে পারে না খালি টাকা টাকা করাে সালারা সব খালি টাকার লুবি,0,sports
বাংলাদেশ টিকেট কে দংখষো করে দিবে,0,sports
চামচামি বাদ দেন।,0,sports
তোর মুখ আর আমার জুতা,0,sports
হায়রে বাঙালি মহানবী কে গালি দিলে তোর বুক কাপেনা আর সাধারণ মানুষ কে গালী দিলে !!!!,0,sports
তোমার কাছে এমনটা আশা করি নাই তাসকিন ভাই ভিডিওটা দেখার মনে হয় এই ভাবে যদি তোমাকে মারা হত তাহলে বুঝতা তোমার মত এমন নোংরা মানুষকে জুতা মারা উচিত অন্য কিছু নিয়ে ফান করতে পারতা,0,sports
সাকিব শাহী শাস্তির বিষয়ে আগেই আঁচ করতে পেরে ম শ্রেণীর ক্রিকেটারদের নিয়ে দাবী আদায়ের আন্দোলনে নেতৃত্ব দিতে বিনা উস্কানিতে মাঠে নেমেছিল। সাকিব শাহী আয়কর ফাঁকি দেওয়া শত কোটি টাকার মালিক হলেও রাত্রিকালীন জাতীয় নির্বাচনের আগে নৌকা মার্কার সমর্থনে ভোট চেয়ে ঘটনা কোন রকমে ধামাচাপা দিতে সমর্থ হয়েছিলে । কিন্তু আওয়ামী লীগ সমর্থিত বিসিবি ঘটনা সুরাহা করতে রাজি না হলে সে ক্রিকেটারদের নিয়ে রাজপথে নেমে ধর্মঘটের ডাক দেয়। সাকিব শাহীকে কেন কর ফাঁকির অভিযোগে রাজস্ব বিভাগ কর্তৃক জিজ্ঞাসাবাদ করা হবে না তার কারন দর্শাতে আইনি নোটিস জারি করা হোক।,0,sports
রাসেল মুসলিম রাসেল ইনশাআল্লাহ বলছে এতেই আমরা খুশি বিপিএল খেলে দেখে যতখানি না খুশি হয়েছি তার চেয়ে বেশি খুশি হলাম ইনশাআল্লাহ বলাতে😍,0,sports
সাকিব কে নিষিদ্ধ করলে আর খেলাই দেখবোনা জিবনেও বাংলাদেশের।।,0,sports
পাপনকে হটাও মিথ্যাবাদী,0,sports
তুমি দুর্জয় তুমি দুর্বারতোমায় রুখবে কে ?এ সাধ্য কার !!,0,sports
ধারাবাহিক চাই ফিজ ❤,0,sports
অনেক সুন্দর লাগলো ভাই! আমিও বড় হয়ে ইনশাল্লাহ আপনার মত হবো,0,sports
মুশফিক কি ওরে গালি দিলে কি হয়। আর বাংলাদেশে শাট পরা মাদারীর সুদ দালাল। বাংলাদেশের টাকা সালার পুতরা বসে বসে লাখ টাকা লাখ বেতন পাই,0,sports
"জানি না, কেন জানি হ্যাপির মূখ দেখে মনে হলো,সে রুবেল কে কিছুটা হলেও ভালবাসত ।",0,sports
করি,0,sports
আশ্রাফুল শেষ সাকিব শুরু,0,sports
ইমরুল ভাই যত ওই ভালো খেলক কিন্তু জাতীয় দলে খেলার জন্য চান্স দিব না শালারা,0,sports
সাধারণ মানুষ ভাত পায় না আর ওদের নাকি সেলারি বাড়াতে হবে এত টাকা দিয়ে করে কি ওরা,0,sports
শালা তদের কারণে বাংলাদেশের এই অবস্থায়,0,sports
সাব্বির জেটা করেছে ঠিক করছে,0,sports
জারা জারা আমার মতো ভাইকে ভালোবাসেন মন থেকে সুধু তারাই লাইক👍👍👍দিবেন 💜💜💜💜 😍😍,0,sports
এখানে মেনেজমেন্টের সব নাটকবাজ আর মিথ্যাবাদী,0,sports
সব জায়গায় শালার দুর্নীতি। জনগণের টাকা লুটে পুটে শেষ করে দিচ্ছে।আমরা প্রবাসীরা দেশের এই দৃশ্য দেখে হতাশ হওয়া ছাড়া করার কিছু নাই।,0,sports
গেইল ও অনেক ভাল খেলছে অসাধারণ 😍😍,0,sports
বারতে পাপন কে আর পাপনের বাপকে পাটানো দরকার বারতে,0,sports
এত দিন কেন চুপ ছিলেন।আনন্দলনের পর কেন আসলো এই ঘটনা।,0,sports
টাইটেলটা ঠিক করার অনুরোধ রইল। আমি প্রথমে কনফিউজড হয়ে গিয়েছিলাম।,0,sports
গভীর ষড়যন্র,0,sports
ইসলামিক ভিডিও দেখতে একবার ক্লিক করুন,0,sports
দুইবছরপাপন কোথাই ছিল,0,sports
এটা খেলা না শয়তান একজন আরেক জনকে আঘাত করে পাগল এটা নাকি খেলা,0,sports
পাপ হটাওক্রিকেট বাঁচাও,0,sports
সবচে বড়ো খতি হবেআর বাংলাদেশ থেকে ক্রিকেট টা হয়তো চিরো তরে হারাবে,0,sports
একজনে সিলি নিয়া খেলতে নামে না বলিং এ না ব্যাটিং এ,0,sports
দুইটা খারাপ,0,sports
আমরা কারো দোষ না ধরি নিজেক বদলাই নিজে বালো হই আমিন 🤔🤔,0,sports
এটা কি সত্যিকারের রুবেল???,0,sports
"সাব্বির আমার অহংকার, আমার গর্ব কারন I love him.",0,sports
মুস্তাফিজ নট আউট বা দেখে খুব ভাল লাগল তার কাছ থেকে জহরুলের ব্যাটিং শিখা দরকার,0,sports
সাকিব কে ছাড়া তো খেলা দেখতে ইচ্ছে করেনা,0,sports
পাপনকে ধাক্কা দিয়ে বের করে দেওয়া হক কি বলেন ভাইয়েরা,0,sports
রুবেল বাংলেদেশের ১ নাম্বার বল্লার,0,sports
এতো পাগল কেনো আপনি ভাই,0,sports
সাকিবের চোখ বলেআমি বলির পাঠা বনে গেছিআমাকে ক্ষমা করে দিও তোমরা;,0,sports
ভাল খেলছে,0,sports
সাকিবের ও দোষ কম নাই!!!বেশি খেতে চাইলে অল্পের লাগলও পায়না।,0,sports
পাপনের পদত্যাগ চাই কারা কারা হাত উঠাও।শালা ক্যাসিনোর জুয়া খুর মাদারির বাচ্চারা এসব জাগায় চান্স পায় কিভাবে?,0,sports
হট যিনিষ চোখে পড়ায় ওর মাথা নষ্ট হয়ে গেছে কি আর বলার😝😝,0,sports
"সময় টিভি কে ধন্যবাদ সব সংবাদ সুন্দর ভাবে তুলে ধরার জন্য। পারলে অার একটা ভাল কাজ করেন, সেটা হল এই মাদার চোদ ক্রিকেটারের ডিএনএ টেষ্ট করেন।কারন এই শালা একের পর এক ভ্যাজাল করেই চলেছে। ১০০% ভাগ গ্যারান্টি এর গোড়ায় গন্ডগোল।",0,sports
বোর্ড প্রেসিডেন্ট ইন্ডিভিজুয়ালি প্লেয়ারদের নিয়ে প্রেসের সামনে এভাবে সবকিছু নিয়ে কথা বললে কি বালটা হবে।এসব ভেতরের জিনিস ভেতরেই তো থাকা উচিত।সামান্য প্রেস সামলানোর যোগ্যতা নাইএরা চলে আসে বোর্ড প্রেসিডেন্ট হিসেবে,0,sports
পাপন নিকৃষ্ট !!,0,sports
ঢাকা বাদ আমি অনেক খুশি কারন ঢাকা বেসি গরবো করে আজ ঢাকার সব অহংকার শেষ,0,sports
ফালতু রুভেল ও নাসির মেয়েদের নিয়ে খেলা বাদ দেও,0,sports
পাপনের বগা কাটা দরকার এখন,0,sports
আমি ইউটিউবে নতুন সবাই আমার চ্যানেল সাবসক্রাইব করেন আমি ও করবো,0,sports
মেহেদী 💓💓,0,sports
সব দোষ বিচিবির আবাল মার্কা কর্মকর্তারহ্লার পুত্রা ভালো প্লেয়ার তো আনতেই পারেনাবরং যা ছিলো তাদেরকেও ধ্বংস করে দিছে,0,sports
নুনু দারিয়ে গেলে কি হবে,0,sports
এতো কথা বলার কি দরকার বুল করলে বুলের মাসুল দিতে হয় এটাই সত্যি,0,sports
কেউ কি লক্ষ্য করেছেন যে এ কুমিল্লা এর রান তখন একটা সিঙ্গেল হয় আর রান হয়ে যায় তার মানি কুমিল্লা করে নেই করছে এইরকম যদি বাজে গ্রাফিক্স হয় যেই গ্রাফিক্সের প্লেয়ারদের রান বাড়িয়ে দেওয়া হয় ও টিম টোটাল বাড়িয়ে দেওয়া হয় তাহলে তো এইটা কোনো প্রিমিয়ার লিগ এর যোগ্যতা রাখেনা,0,sports
সাকিবের উচিত এই বেঈমান দেশে আর না খেলা,0,sports
আমরা কোটি ঞিকেট পেমিক দশক সাকিবের পাশে সাথে আছি তবে দুই বছর সাকিবের খেলা দেখতে পারবো বর দুঃখের কষ্ট চাপা রয়লো বুকে,0,sports
সমস্যা নাই মাসের জন্য বাংলাদেশের খেলা দেখাই বন্ধ করে দিবো।।,0,sports
আমি প্রথম দেখলাম,0,sports
সব সময় যে জয় হবে তা না হার জোয় নিয়ে আমরা আছি team Bangladesh et Sathe,0,sports
আমার যতদুর মনে পড়ে তামিম একবার এমন সেলিব্রেশন করেছিল।তখন তো এমন কনো কথা হয়নি,0,sports
গর্ব হচ্ছে রাসেলকে নিয়ে ইনশাল্লাহ বলার জন্য। সেলুট ব্রাদার,0,sports
পাগল এ সব ভুল ভাল খবর কে দেয়??? :,0,sports
টিনের চালে ক্রো সবার সেরা ইম্রুল ব্রো🤣🐸🤣🐸,0,sports
আমরা বাঙালিরা এরকমই ভাই সাব্বিরের এতদিন ফ্রম ছিল না এর জন্য দায়ী কে আমরা,0,sports
মুশফিকের জাসি্ পরা লোকটার কারনে ভদ্র লোকটাকে করা হলো আসলে লোকটা সত্যি কথা বলছে।,0,sports
আমাবর্সার চাঁদ 🙄🙄,0,sports
যদিও আমি একজন সিলেটি তার পরেও আমি চাই মুশি ভাইয়ের হাতে কাপটা উটুক,0,sports
মুশফিকুর রহিম বেস্ট ইস বস্,0,sports
মুশফিক এর সাতে আমাদের প্রিয় নবী হযরত মুহাম্মদ সাল্লাল্লাহু আলাইহি ওয়াসাল্লাম তুলনা করা ঠিক না,0,sports
​পাপনের পদত্যাগ চাই।,0,sports
পাপনের পদতেগ কে কে চাও সারা দাও ।,0,sports
আমরা জার মান নাই তাকে মানোনিয় বলে নিজেদের দংশ নিজেরা ডেকে নিয়ে আস্তাসি।আপনারাই বলেন আমরা জানি সে মুসলিম কিন্তু সে বলে মা দুর্গা আসলে নাকি দেশ ফসলে ভরে যায় কোনো মুসলিম এ কথা বলতে পারে। এরপর দেখেন দেশে নেয়ের অনিয়মের বিপক্ষে আনন্দলন করলে তা যদি সরকারের বিপক্ষে যায় তাহলে আপনি সেস। গত বসর জাবদ কেউ ভোট দিতে পারেনি দিতে দেয়নি তার আবার মান থাকে কি ভাবে । সে আমাদের মুসলমানদের লজ্জার। তেকে মাননীয় বলা যাবে না,0,sports
।জন্যজস্কক্সমিচকেও,0,sports
যারা সাকিব কে ভালবাসেন তারা লাইক করুন প্লিজ😍,0,sports
নাসির এর খেলা খুব ভালো বোলেই আজ দেশবাসী তাকে এক নামে চিনে।। (কথায় আছে এক মোন দুধে এক ফোটা চুন!😱 ব্যাস ! সব শেষ 😭) এতোটুকুই বলবো নাসির ভাই তওবা করে খেলায় মন দেন মেয়েদের সম্মান করুন।মেয়েরা বেবহারের পণ্য নয়।। সব মেয়ে এক না।। আপনি নানা রকম মেয়েদের করে ভুল ও পাপ করেছেন।সুভা সেই পাপের সাজা।।আল্লাহ্ আপনাকে মাপ করুন।।।,0,sports
বিপিএল সাউন্ড সিস্টেমের মতো এতো পেইন জিনিস আর জগতে নাই,0,sports
"সাব্বিরের জীবনের প্রথম শতক,তো উজ্জাবন তো একটু করবেই প্রথম সেঞ্চুরি",0,sports
এটা পাপনের কিছু জানত আপন নীরবে আছে কেন শাকিবের অন্যায়টি পাপন এটার ব্যাখ্যা দেয় না কেন তাপন চাইছে শাকিব যেন না খেলতে পারে পাপন নিজের স্বার্থে নাসিরকে টিকেট থেকে বাইরা রাখছে অনেকদিন এখন আবার নিজের স্বার্থে আঘাত আরসে তাই সাকিবকে খেলা থেকে বের করে দিছে পাপন বাংলাদেশের জনগণ আপনার যাদের চোখে ধোকা দিছে পাপন,0,sports
অতিথি মহোদয় বর্তমান ক্রিকেট অঙ্গনে মুখোশের আড়ালে দুর্নীতি গুলি স্পষ্ট ভাবে তুলে ধরছেন। পাপন সাহেবের বন্ধু যদি ক্যাসিনো মালিক লোকমান হন তাহলে বাংলাদেশ ক্রিকেট বোর্ড তথা দলের আগামীতে ধ্বংস অনিবার্য। এদায় থেকে মুক্ত হতে হলে বর্তমান বিসিবির প্রধানদেরকে নির্বাসনে দিতে হবে।,0,sports
এই কাজটা কখনোই ভালো হয় নাই তাসকিনের থেকে এটা কখনোই আশা করা যায় না,0,sports
বাংলাদেশ ক্রিকেট ধ্বংসের মুখে ঠেলে দিচ্ছে এই পাপকন বছর আগে জানতেন না যখন সেই আপনাদের লুটপাট সম্পর্কে আন্দোলন করলো তখন তাকে তাদের লুটপাট এর রাস্তা পরিষ্কার করার জন্য সাকিবের বিরুদ্ধে অভিযোগ গঠন করছেন তাকে নিষিদ্ধ করেছেন ভালো বাংলাদেশ ক্রিকেট ধ্বংসের মুখে ঠেলে দিয়েছেন ।,0,sports
কখনো বিয়ে করবে না কিন্তু বিয়ে ছাড়াই বছর বছর বাচ্চা নিবে,0,sports
টাইগারদের জয় সব সময় ।।,0,sports
সাকিব ছাড়া খেলা কে ঐ ভুলে যাবো!!,0,sports
আমরা দেশবাসী পাপনের পদত্যাগ চাইহেরে আর সভাপতি হিসাবে দেখতে চাইনা,0,sports
ভাই সত্যি আপনাকে অনেক অনেক স্যালুট সত্য গুলো তুলে দরার জন্য??? ভালোবাসা♥ অবিরাম প্রিয় সাকিব আল হাসান ভাই✌😍পাপনের পদত্যাগ চাই,0,sports
"দেশের দূর্নাম করতে ছারে নাই,কত ছোট মনের মানুষ",0,sports
"কেও অভিযোগ করলেই দেশের সম্পদ কে নিষিদ্ধ করা বোকামি,, <br /> আমি পাকিস্তান কেও ভালোবাসি তবে প্রথমে বাংলাদেশ জিন্দাবাদ।",0,sports
যাক ক্রিকেটটাও ধ্বংশ হতে যাচ্ছে।,0,sports
চালাকি করে ছুটি নিলো নাতো?,0,sports
সাকিব কে ফাসান হষেসে,0,sports
পাপন ভাজা জিবীনে যদি ক্রিকেট খেলতি তাহলে তোর মুখ দিয়ে এমন কথা আসতো না,0,sports
জুতা মার তালে তালে পাপনের গালে,0,sports
সাববির😁,0,sports
পাপন চোর ও কটি কটি টাকা মেরে খায়,0,sports
সাবাস দস্ত😂🔥🙏,0,sports
মুশফিক ডানহাতি না হয়ে বা হাতি হলেই ভালো হতো,0,sports
জামালপুর ডিসির কথা মনে পরে গেল 🤪🤪🤪,0,sports
আমাদের বাংলাদেশের মানুষের কাজি মানুষ কে নিয়ে সমালোচনা করা,0,sports
মুজা পাইলাম,0,sports
নোটিফিকেশন পাওয়ার সাথে সাথে কারা ভিডিও দেখো??,0,sports
ম্যান অফ দ্যা ম্যাচ কে হইছে কারো জানা থাকলে বইলেন,0,sports
সত্যিই আজকের খেলাটা দারুন হয়েছে!!,0,sports
এইটা কোনো কাজ হইলো😪😪😪😪,0,sports
গালি দিব নাত কি করব,0,sports
খুব খারাপ লাগে যখন দেশি খেলোয়াড়েরা ভালো খেলে দাম পায়না,0,sports
"মাশরাফি তো নিজে খুব বড় বাল ফালাইছে,,,,,আর সাব্বির celebrate করলেই দোষ",0,sports
তাসকিন ভাই তোর জন্য আফসুশ হয় জেই বল করোস? জাতিয় দলে তো আর চান্স পাবিনা চটপটি ওয়ালাদের সাথে থাকবি তোর ব্যাবসা তো আসেই ইউটিউব টাকা ইনকাম করবি????? বাংলাদেসর তে জেই টাকা নিসোস এডি ফিরত দিবি জত লম্বা তত বলদ,0,sports
উচিত কথায় বন্ধু বেজার গরম ভাতে বিলাই। খেলা চুদাইতে পারেনে আবার ভাব,0,sports
হোপ ব্যাডা।এইগুলো কি ফাউল নিউজ দিচ্ছিস।আর বাকি পাবলিক ও সেই তালে নাচতেছে।আজিব মানুষজন এরা,0,sports
ভাই এটা ইন্ডিয়ার চাল,0,sports
"ভুল করছেন, অভিশাপ লাগবেই",0,sports
এইগুলো কিছুই না আসলে আমাদের পা পোন্দা নটির ছেলে নিজের ক্ষোভ ঝারার জন্য সাকিব কে ফাসিয়েছে কেননা সাকিবের নেতৃত্বে ক্রিকেটার রা আন্দোলন করেছে।,0,sports
ভাই অনাই করলে শাচতি পেতে হবে,0,sports
সবাই আমার চেনেলে গিয়ে ঘুরে আস।,0,sports
মুশির জন্য বুকের বাম পাশে ব্যথা করছে,0,sports
এগলো ঠিক না ভাই।এসব আজে বাজে ভিডিও পোস্ট করে অন্নের গালি না খেয়ে ভালো কিছু পোস্ট করুন সবাই ভালো বলবে।,0,sports
মুশফিক বস তো সবচেয়ে বেশি ধারাবাহিক,0,sports
"এই হারামজাদা শয়তানের জারজ মানুষের ট্যাক্সের টাকায় মাগীবাজি করে আর খেলার মাঠে দেশের পাছায় বাঁশ দেয়। এই সব জারজদের রাস্তায় পিটায়ে মেরে কুত্তা দিয়ে খাওয়ানো দরকার। সব টাকা আর সম্পত্তি বাজেয়াপ্ত করা দরকার। দেশে এত ভাল ক্রিকেটার থাক্ষে সিলেকসন কমিটি কোথা থেকে এই সব জারজদের খুজে পায় , তা তারা ভালই জানে।",0,sports
হুমায়ূন কবির রোজ। রোজ তো টাইটানিকের নায়িকা। নিউজ করার আর জিনিস পায়নায়,0,sports
হাতে গনা কএটা পিলিয়ার আছে পুরান ওরা চাল করে নতুন কিছু বালো পিলিয়ার। সরানর জন্য এই নাটক। নতুন গুুলা যদি বালো করে তাহলে পুরান গুুলা বাদ পরবে।,0,sports
সাকিব তুমি বাংলাদেশী কিন্তু বাংলাদেশের কলুষিত রাজনীতি টা জানলে না🤔,0,sports
পাকিস্তানিরা ভালো করছে,0,sports
মুশফিকের হাতে ট্রফিটা না যাওয়াতে কার কার খারাপ লাগছে লাইক দিয়ে জানিয়ে দিন ?? 👍🖐👍,0,sports
সিলেটের এই দুই দানব আজকা একটু হাই হয়ে গেছিলো😂। আর সবাই আমাকে শুধু একটা সাহায্য করেন চ্যানেল ভিসিট করতে পারেন আর ভালো লাগলে সাবস্ক্রাইব করুন,0,sports
সাকিব ছাড়া বাংলাদেশ মৃত সাকিব কে খমা করে দেওয়া উচিত সাকিব কে ফাসিয়েছে বাংলাদেশ বোড সাকিবের জন্য আমি বাংলাদেশ টিমকে সাফোট,0,sports
আমি শিওর বলতে পারি বিসিবি এখন রংমহলের প্রশিহ্মন দেয়। আর ক্লাব গুলু হচ্ছে সুতিকাগার। না হলে একটা ক্রীকেটার এত খারাপ কেন হবে।,0,sports
দফা আন্দলোন করে ছিলতার নেতা ছিল সাকিব এটাই তার দোষ।সাকিব ভাই আমরা আছি তোমার সাথে।,0,sports
নাটকটা দেখবেন,0,sports
সামলাও ঠেলাবুঝবা পরে😡😡,0,sports
সাকিব কে বাদ দিলে ক্রিকেটে খতি হবে সাকিবের খতি হবে না,0,sports
"সাব্বিরেরা কি মঙ্গল গ্রহ থেকে আসছে!!!!আমাদের মধ্যে থেকেই কেউ না কেউ এই সাব্বিরেরা।<br />আমাদের আসে পাশে দেখলেই এসব হরহামেশাই দেখা মেলে,একাধিক সম্পর্ক যা বনিবনা বা ভবিষ্যত জিবন তাদের সাথে চলার নেতিবাচক আভাস পাবার জন্যে ভাঙ্গে না,আগে থেকে প্রিপ্লান থাকে,,,,,,,স্টার হবার পর এমন হয় না,স্টার হবার পর মাত্রটা ছাড়ায়,বেপরোয়া হয়,মেয়েরাও নির্ভরতা খোজে আবার কারো মাঝে লোভ সবমিলিয়ে একজন স্টার মাঝে জুটতে থাকে বহ্নিপতঙ্গ,,,,,,, শহর থেকে গ্রাম আর সমাজের সর্ব স্তরের মানুষের মাঝে এই জিনিষগুলো বিদ্যমান,,,,,সুখ ও শান্তির সমাজ গড়তে আমাদের এই একাধিক সম্পর্ক,পরক্রিয়া আর জেনা থেকে না সরে আসতে পারলে সমস্যাগুলো আমদের পিছু ছাড়বে না,,,,,,,,,<br />এরা আমাদের মধ্যেরই কেউ না কেউ স্টার হবার পর মাত্রা ছড়ায়,এই যা,,,,,,,",0,sports
এটা ইন্ডিয়ার একটা ছাল,0,sports
আমি যেতে চাই জডানে,0,sports
পাপন কে বিতাড়িত করতে হবে কারা একমত,0,sports
বলে বলছে কি হছে বাল।,0,sports
রাইট ভাইয়া,0,sports
পাপ তার বাপকেও ছাড়ে না আজ না হোক কাল এর শাস্তি সে অবশ্যই পাবে,0,sports
আসলে যে বানচোদ রা ভুল ভিডিও ছারে তাদের কে জুতা মারা দরকার,0,sports
দালাল,0,sports
সাব্বির ভাই এগিয়ে যাও আমরা আছি তোমার সাথে,0,sports
পাপন কখনো আপন হয় না,0,sports
সব কিছু জন্য দায়ি সমাজ বা সরকার বা তার বাবা-মা তাকে বিয়ে করিয়ে দিলে এমন কাজ করতো না বা হতো না!🇧🇩,0,sports
বিসিবি কে জুতা মারতে হবেমাস দিতে পারতো,0,sports
লোকটা হয়তো বলছে হয়তো শুনছে বালছিরা।।।ভিডিওটা দেখে এরকমই বুঝলাম,0,sports
ক্রিকেট বোর্ড টা পাপানকে সম্পদ হিসেবে দান করে দিয়েছে।,0,sports
আমার নাম্বার 01733160503 তোমার ফোনে,0,sports
সাকিব বাংলাদেশ ক্রিকেতে খাদ্যে লবণের মত,0,sports
পাপনের সব দুশ,0,sports
পাপ করেছে যে পাপন,0,sports
একটা ক্রিকেট বোর্ড ধ্বংস করার জন্য এক পাপনই যথেষ্ট।,0,sports
ভাই সাকিব জন্য কষ্ট লাগছে 😥😥😥,0,sports
ম্যাচ হারছে রাসেলের ক্যাপন্টেনসির জন্য।। টস জিতে ফিল্ডিং নেয় কেন?? রান চেজ করার মত ব্যাটিং নেই তবুও ফিল্ডিং নেয়।।ওভার কনফিডেন্ট ডুবাইচে,0,sports
ছেলেটাকে একটা বিয়ে করিয়ে দিলেই হয়......,0,sports
ধন্যবাদ খুলনা টিম,0,sports
একজন অতিরিক্ত ফিল্ডার হিসাবে নেমে টা ক্যাচ ধরা ’ জাকির আলী,0,sports
সাকিব আন্দোলনের নেতৃত্ব দেয়াতে ওকে আজকে এই শাস্তি দেয়া হল।এতে আমাদের ক্রিকেট এরই ক্ষতি হয়েছে।আর লাভ হয়েছে পাপনের।,0,sports
পাপন দাদা আগামীতে ভারত কে জয় দেওয়ার জন্যসাকিব কে বাঁশ দিলো।শুধু সাকিব কে নয়পুরো বাংলাদেশ বাঁশ খেলো,0,sports
এই হল বাংলাদেশের নাটক শবাই তা বুজতে পারে,0,sports
পাপন হয়েছে ভারতের দালাল ।,0,sports
ওভার এ রান ভাবা জাএ 😥,0,sports
ভাই আপ্নের কথা গুলা খুবই ভালো লাগলো।সাকিব জাতে ভারত এর সাথে না খেলতে পারেএটা ভারত এর একটা সরজন্ত্র😥😡,0,sports
খালি এটা দাও ওটা দাও পার্ফরমেন্সের নামে খবর নাইআফগানিস্তানের সাথে টেস্ট হারবিশ্বকাপে ব্যার্থতাবার বার ভারতের কাছে জিতা ম্যাচ হারাএখন পর্যন্ত কোন ট্রফি অর্জন নাই আসছে বেতন লাখ নিতে বাল ছাল,0,sports
প্রায় প্রতি বার পয়েন্ট টপবিলের তলানিতে থেকে যে দলটা টুনামেন্ট শেষ করে। তারাই মনে হচ্ছে এই সিজনের চ্যাম্পিয়ন হবার দাবি দার। শুভ কামনা রইলো খুলনা রাজশাহী চিটাগাং এর জন্য।,0,sports
হায়রে মানুষ আরও বছর পিছিয়ে গেলাম,0,sports
দিনের বেলায় গ্যালারি ফাঁকা আর অথচ লক্ষীপুর হায়দার গঞ্জ ভোর চারটা পর্যন্ত লাখ লাখ মুসল্লি তাফসীরুল কোরআন মাহফিল শুনেছে ইনশাআল্লাহ এটাই ইসলামের বিজয় একদিন হবে,0,sports
ভিডিও হৈছে অপেক্ষা করছিলাম,0,sports
স্যামসাং উত্তর বাচ্চারা এরকম ব্যবহার করতেছিস কেন,0,sports
এর অনূর্ধ বিশ্বকাপ খেলা দেখলেই বুঝতে পারা যাবে সে কত ঠান্ডা মাথার খেলোয়াড়।,0,sports
টাইগার ভক্তরা কই লাইক হবে।,0,sports
সাব্বির একজন ভালো ব্যাটসম্যান ভারতীয় মিডিয়ার কথায় তাকে এতো বড় শাস্তি না দিয়ে জরিপানা করা হোক।,0,sports
তাসকিন এ খেলায় অংশ গ্রহণ করলে ও দুটি থাপ্পড় খাইলে আমরা আরো বেশি মজা পাইতাম ভিডিও টি দেইখা আবাল একটা তাসকিন,0,sports
ওয় ভুল করছে তাই ওকে সুজুক দাওয়া উচিত,0,sports
একটু বেশি হয়ে গেল না মুশফিকের!! মনে হয় গায়ে চর্বি হয়ে গেছে! আর শালা গাঁজাকোরের কথাও শুনলাম সে ঐখানেই বসা ছিল কিন্তু কি বলছে হুনে নাই কিন্তু খারাপ কিছু বলছে তার গাঁজাকোরের কথা। আসলে কি বলব ভালো প্লেয়ারটার এত খারাপ চরিত্র খারাপটার না জানি কত খারাপ!!!,0,sports
পাপন সাহেবেরা কত কি না পারে।,0,sports
বালের খেলোয়াড় দের বসিয়ে পুরা দল টা কোচ নিজ দায়িত্ব যেদিন থেকে সাজা বে সে দিন থেকে দল ভালো করবে।হেড কোচ নিয়োগের দরকার কি যোদি দলের খেলোয়াড় বি সি বির সদস্যদের সিদ্ধান্ত দল ঘোষনা করতে হয়।বাংলাদেশ দলের হেডকোচের দায়িত্ব বি সি বি কে দেওয়া দরকার,0,sports
আচ্ছা আপনি কি মানুষ না অন্য কিছু। জনগণের এত অশ্লীল কথা বার্তা আপনার গায়ে একটু লাগে না।,0,sports
পাপনরে লাথি মাইরা দেশ থেকে বের করে দেওয়া উচিত,0,sports
তাসকিন ভাইয়া এইটা আবার কি পতিযোগিতা দেখালেন,0,sports
বাংলাদেশের ক্রিকেট এই পাপন কমিটি ধ্বংস করে যাবে। ইনশাআল্লাহ,0,sports
সাকিব পিচ,0,sports
পাপকে জুতা মার সবাই,0,sports
সাকিব বক্তদের জুয়াডি পাপনের বিরুদ্ধে মাঠে নামা উচিত,0,sports
পাপনকে শাস্তি দেওয়ার জন্য আবেদন করা হলো পাপন ম্যাচ ফিক্সিং করেছে এবং ভালো ভালো প্লেয়ার কে শাস্তি দিয়েছে পাপন বরিষ্কারকরা উচিত সাকিব ভাই আমাদের টিমের খেলা শাকিব ছাড়া দেশ অচল বিসিবি পাপন কে জুতা মারা উচিত,0,sports
আজকে বিপিএলে এই প্রথম এতো টান টান খেলা দেখলাম।আসলেই আজকের ম্যাচ অনেক বেশি ভালো লেগেছে,0,sports
খেলা অন্নেক ভাল লাগে চরিত্র টা ঠিক করার জন্য একজন পারফেক্ট লেডিস মেকানিক নিয়োগ করে দেন,0,sports
বাংলাদেশের খেলোয়াড়রানাকি আন্দোলনে নামছেতাদের এইটা লাগবে অইটালাগবে বেতন বাড়াতে হবেএইটা সেইটা। আমি বলি এতসুযোগ সুবিধা পাওয়ার পরেওযদি তারা আন্দোলন করে তাহলেআমার কথা হল এত দিন ধরে এতকিছু পাওয়ার পরে সেই পরিমানকিছুই তো দিতে পারলেন না। রানকরতে যেয়ে জন আউট হয়ে যান।আর আমরা কষ্টে মরি।পাপনের কথার সাথে আমি একমত। হঠাৎ কি মনে করে এই আন্দোলন,0,sports
নাজমুল হাছান পাপনকে আজীবনের জন্য ক্রিকেট বোর্ড থেকে নিষিদ্ধ করা হক যারা যারা লাইক দিয়ে সাথে থাকুন,0,sports
মোমিনুল এত বড় বড় ছয় মারতে পারে তাই তো জানতাম না।,0,sports
সাকিব ভাই পাপন এর গালে একটা থাপ্পর দিয়া খেলা চাইরা দিতেনদেখতেন মাস পর বাংলাদেশ জিম্বাবুয়ের মত হইত,0,sports
পাপোন্দার অনেক লাভ হয়েছে তার সাথে কেউ আর কামেলা করবে না,0,sports
বাংলাদেশ ক্রিকেটকে ধ্বংস করার চেষ্টা করতেছে এই পাপন কুকুরের বাচ্চা এ কুকুরের বাচ্চা যদি এক বাপের ছেলে হয় তাহলে অবশ্যই পদত্যাগ করবে আর যদি জারক সন্তান হয় তাহলে টাকা লোভে পদত্যাগ করবে না,0,sports
আমি হলে এখানে পদ্যত্যাগ করতাম আর খেলতাম না ক্রিকেট,0,sports
আপনারা কেউ যদি বাংলাদেশ এর ফাস্ট বোলার দের সেরা দেখতে চান তাহলে নিচের লিঙ্ক এ ক্লিক করুন আর লাইক ও কমেন্ট করতে ভুবেন না কিন্তু!,0,sports
সাব্বিরের প্রথম 100 উৎজাপন করতেই পারে সেটা নিয়ে এত আলোচনা কেন ভুজলাম না।,0,sports
যারা সলমন খান সনু নিগম গেছে বলে ভারত কে অপমান করছেন তাদের জানা আছে কি এ ভারতের সাহায্যের কথা ভারত সাহায্যের হাত না বাড়ালে আজ বাংলাদেশ টাই গঠিত হোত না!! আমি ও বাঙালী এবং বাংলাদেশ এর প্রতি প্রগাঢ় ভালোবাসা ও রয়েছে কিন্তু ভারতীয় শিল্পী কে ডাকা নিয়ে সেটা তোমাদের সরকারের দোষ দোষ দিতে হলে সরকার কে দাও শেখ হাসিনা এর কাছে হিসেব চাও খামোখা ভারতকে গালাগাল দিয়ে ভারত বাংলাদেশ এর সম্প্রতি কে আঘাত করবেন না!! 🇮🇳 🇧🇩,0,sports
যারা রুবেলকে নিয়ে গালাগালি করতেছেন রুবেলকে যদি সামনে পান তাহলে কুত্তার মত দল বেঁধে এসে বলবেন ভাই একটা অটোগ্রাফ একটা সেলফি ভাল হন মানুষকে সম্মান করতে শিখেন আমি একজন বাংলাদেশী ক্রিকেটারের ভক্ত আপনাদের বাজে কমেন্ট দেখে এই কথাগুলো বলতে বাধ্য হলাম পারলে ক্ষমা করবেন,0,sports
জিও বস,0,sports
দোষি কে না ধরে নিরঅপরাধ খেলোয়ার কে সাজা দেওয়া হল এতে পাপনের হাত আছে কারণ সে আগে থেকেই বলে রেখেছিল,0,sports
বাংলাদেশের খেলোয়ারা টাকার লোভে পড়ছে।অতিরক্ত টাকা হলে মানুষ খারাপ হয়ে যায়।আগের খেলোয়ারা কত টাকা পেত।আর এখনকার খেলোয়ারা কত টাকা পায়।রাতে দিনে পারাক।আপনারা লক্ষন করুনখেলোয়ারা কি রকম গাড়ীতে চেলাফেরা করে।সিনিয়ার খেলোয়ার একজনে কত টাকা আছেআপনারা জেনে নেয়।খেলোয়ারা কি বাল খেলে।পাপনের সাথে আমি একমত।,0,sports
হিহিহি 👙🐸🐸😂,0,sports
ভাই ক্রিকেট বাদ! এখন এদের এভয়েড করেন! এত টাকা পায় ক্রিকেটারা তা ও তারা খুশী না¡!!!¡ আমরা ফুটবল প্রেমি ক্রিকেটে গুলি মারি,0,sports
ভালো হয়নি,0,sports
মিডিয়ার মারে চুদি,0,sports
গালি আমি দিবো মাদারী,0,sports
কে যেন বলেছিল বিপিএলে রাসেলের ডায়রিয়া হয়ে যায়।।।😁সে দয়া করে আমাকে একটু রিপ্লাই দেবেন।। 😐,0,sports
কোন টিভি নিউজে আসেনাই আশরাফুল মারা গেছে। জীবনে ভালো কিছু করবেন নয়তো আখিরাতে প্রস্তাতে হবে।সবাই খারাপ খারাপ লিখল আমি লিখলাম না।,0,sports
সাব্বির একটি ফালতু খেলুয়ার।,0,sports
গাধার সাথে ভাব মিশিয়ে খেলে যা হয় আরকি 😠,0,sports
কই বে ফইটক্যা কুনঠে গেলি বে দ্যাখবে হারঘে রাজশাহী জিতেছে।😍😍,0,sports
পায় আৰু কিশোৰ কুমাৰৰ নাম আছিল আৰিয়ানা নিয়ন্ত্ৰণ ৰিছিল কৰা হয় কাৰণ ইহঁতৰ কেইবা বছৰ বয়সতে তেওঁ দ্বিতীয়বাৰৰ কাৰণে প্ৰধানমন্ত্ৰী নৰেন্দ্ৰ মোদী এই অঞ্চলত অসমীয়া লোকে বিহুত আৰু সন্মানসূচক ভাৱে তেওঁক তেওঁৰ ইচ্ছানুসৰি মহম্মদ ৰফি আৰু লতা মংগেশকাৰৰ আৰু কিশোৰ কুমাৰে নানা অত্যাচাৰৰ বলি কটা কলপাত এই কথা দেখা যায় কিন্তু ওজন ও অন্যান্য জলচৰ চৰাই এটা অংশ ৰূপে অন্তৰ্ভূক্ত কৰে শঙ্কৰ এই কথা অস্বীকাৰ কৰিলে যাৰ বাবে তেওঁ অৰ্জুনৰ উপৰত আলোকপাত আৰু কিশোৰ নৰসিংহ নামৰ এটা কবিতা আৰু গল্প লিখাৰ আগতে পুৰণি প্ৰবন্ধ এটাত উপশ্ৰেণী কৰে আৰু গল্প লিখাৰ এসপ্তাহৰ পিছত তেওঁ দ্বিতীয়বাৰৰ এই অঞ্চলত অনেক মচজিদ আৰু কিশোৰ নৰসিংহ মেহতাৰ আৰু লতা মঙ্গেশকাৰ উভয় দেশৰে নাগৰিক,0,sports
ম্যাও,0,sports
কি বলবো তাসিনেশন ভাইয়া আবেগ টা ধরে রাখতে পারিনা কারণ আমরা তো বাঙালি সেজন্যসেজন্য আমাদের বিশ্বাসেরা একজন প্লেয়ার কে আমরা হারিয়ে ফেলছি একমাত্র একটি লোকের কারণে সে হচ্ছে পাপন পাপীর জন্য!পাপন কে কিভাবে গালি দেবো মুখে ভাষা নেইতারপরও বলছি পাপন তুমি হাসিনার প্রিয় ব্যক্তি হলেও আমাদের কাছে তুমি কিছুই না !কেন তুমি বাংলাদেশের জনগণের ঊর্ধ্বে নওতাই সব বাংলাদেশের ক্রিকেটপ্রেমীদের বলছি সবাই আন্দোলনে নেমে পড়ুনপাপন হাটাও দেশের ক্রিকেট বাঁচাও,0,sports
কি জন্য সাব্বিরকে দলে নেয় 🤑🤑🤑,0,sports
সাকিবের মতো বাংলার রত্ন অ যখন দূরনীতির কবল হতে রেহাই পান নি তখন আর সাধারন মানুষের অবস্তা কোতায়,0,sports
ভালোই ব্যাটিং করতে জানে।,0,sports
সৌম্য হারা ম্যাচ জিতাইসে আজকে।,0,sports
আল্লাহ তোমাদের হেদায়েত দান করুন।আমিন।,0,sports
ভাই এই কথা কি ঠিক এর পমান কি,0,sports
মাসরাফিকে চাই সভাপতি,0,sports
বাংলাদেশের নিউজ চ্যানেল গুলো কোন ভয়ে পাপনের কু কর্ম প্রকাশ করছে না?,0,sports
সম্মান নিয়ে পদত্যাগ করুন।বাংলাদেশ মানুষ অনেক সচেতন এখন😡😡,0,sports
জার জন্য বাংলাদেশ ক্রিকেট আজ বিশ্বের বুকে পরিচিত আজ তাকে নিয়েই রাজনিতি দুনিতি! নপপা সালা,0,sports
দেখতে দেখতে বিপিএল খেলা শেষ,0,sports
মজা দেওয়ার জন্য স্লাপ না দিয়ে এমনিতেই ফান করে মজা দিতে পারতো। অযথা একে অন্যকে ব্যথা দিয়ে এমন মজার মানে হয় না।,0,sports
যমুনা টিভির সাংবাদিক কে বলতেছিজনগনের কমেন্ট গুলো পাপন সাহেব কে দেখান,0,sports
আগামী প্রজন্ম কি শিখবে এদের কাছে? অনেকেই এটা ভাবছেন? <br />আরে ভাই এই প্রজন্মই মুখ দেখাতে পারছি না বহির্বিশ্বে এদের কারণে। অন্য সহকর্মীর স্ত্রীকেও সম্মান দিতে জানে না। এটাও শিখায় নাই ওরে কেউ?,0,sports
সাকিবের জন্য বাংলাদেশের খেলা দেখি কিন্তু এখন সাকিব নাই এখনকি বা দেখমু,0,sports
পাপন মনে হয় মেয়াদোত্তীর্ণ গাজা খাইছে,0,sports
ধুর তোর খেলার মাইরে বাপ আর খেলাই দেখবো না।,0,sports
আমার আপন ভাই নাকি কীছু জানেন নাএটা কী পাগলে বিশ্বাস করবে কী আমার মনে হয় না?,0,sports
এখন সাকিব ধ্বংস হয়ে যাবে।যেমন টা ধ্বংস হয়েছেএক সময়ের দূরদর্শী ব্যাটসম্যান ;মোহাম্মদ অাশরাফুল;,0,sports
ভারতের সাথে খেলার আগে বাতিল করা হলো,0,sports
হালা জুয়ারি,0,sports
এতো খুশির সংবাদ এতো দিন কোন দোষ ছিল না এখন দোষএটাই আমাদের সরকার,0,sports
আমাদের হুমকির মূখে। আল্লাহ ষড়যন্ত্র থেকে আমাদের কে বাঁচান।,0,sports
সবার চেয়ে ভালো করছে ছাব্বির তবে একটু চুপ থাকা উচিত ছিলো।কারণ দল হেরেছে,0,sports
মাশাল্লাহ,0,sports
মুশফিককে গালি দিছে তো কি হয়েছে,0,sports
আল্লাহ্ তুমি এদের বিচার করা,0,sports
মেহেদী অসাধারণ কিছু শট দেখিয়েছে। হাতে মোটামুটি ভালো পাওয়ার আছে,0,sports
সরল সহজ মানুষ পেলে যা হয় আর কি,0,sports
ভাই মাল টা খুব হট,0,sports
পাপনের পদোত্যাগ চাই,0,sports
পাপন সাহেব টিক বলে ছেন,0,sports
তীব্র নিন্দা জানাই আই সি সি এর এমন সিদ্ধান্ত কে।।,0,sports
আশা করি আগামী তে বিপিল টা আর ভাল হবে। একমত হলে কমেন্ট করবেন।,0,sports
আমার মত সব থেকে বাংলা দেশের খুব ভালো প্লেয়ার একদিন বড়ো মাপের প্লেয়ার হবে তবে তাঁকে মন দেয়ে খেলতে হবে সে অনেক কিছু করতে পারবে সাব্বির,0,sports
এটা অতিরিক্ত,0,sports
আমি চাই সাকিব বাংলাদেশ দলে ফিরে আসুক,0,sports
পাপনের মত আহম্মকের কারণে দলের এই অবস্থা। আর এমপি মন্ত্রীরা কেমতে ভাল খেলবে?,0,sports
জ্ঞান পাপীরা ক্ষমতায় গিয়ে সব ধ্বংস করেফেলছে। সুশিক্ষার অভাব হলে যা হয়।শালার যত্তসব,0,sports
"দোষ সবারই কম বেশি থাকে,কিন্তু জাতীয় দলের একজন খেলোয়ার মেয়ে খাওয়ার বেপারে এত লে লে করে কেন।ছি ছি ছি.........",0,sports
বালের দাবি সাকিবের,0,sports
ভাই একদম ঠিক বলছেন। এইখানে আমাদের সাব্বির কে আরো বাহবা দিতে হবে।<br />আর আমাদের চিন্তা ভাবনায় পরিবর্তন আনতে হবে।,0,sports
এখানেও কি তাহলে বিএনপি জামায়াতের চক্রান্ত আছে ।,0,sports
পাপন।সালারে।সব।দায়িত্ব। থেকে।বাদ।দেন।তাহলে।সব।ঠিক।হয়ে।যাবে,0,sports
অখুশি বালো লাগে না,0,sports
সাকিব কোন অপরাধ করেনিআমাদের সম্পদ সেআই সি সি ইন্ডিয়ার গোলাম,0,sports
আমার মনে হয় বাংলাদেশে সরকারি এমন কোন সংস্তা নাই যেখানে দূর্নিতি হয় না,0,sports
মুসফিক এর ফ্যানরা লাইক দিয়ে যাও,0,sports
যেদিন থেকে খেলবে সেদিন থেকে খেলা দেখব,0,sports
তুই পদত্যাগ করলে সব ঠিক হয়ে যাবে।,0,sports
আমি সিয়র ফাকে নিয়ে মানি ব্যাগ রাইখা দিছে,0,sports
বালের কথা এর আগে আশরাফুল কে!! এখন সাকিব!! সাকিবের বালডাও ছিরতে পারবোনা,0,sports
কষ্টের করতো নাকি তোদের কারণে তারা করতাছো আপন কে ছাড়বে দাঁত ফালায় দিমু খানকির পোলা মাদারচোদ বাংলাদেশের ক্রিকেট ধ্বংস করতাছে,0,sports
বাংলাদেশের যত টাকা আছে সব টাকা ক্রিকেটারদের ডেলে দেওয়া হোক ওদের বাবার টাকা,0,sports
মেহেদি হাসান রানা অসাধারন বল। কার কার ভাল লেগেছে,0,sports
ক্রিকেটের ভিতরে যদি রাজনীতির মত এত জল ঢুকে যায় তাহলে কি হবে আর ক্রিকেটের হয়তো এটা আমার বোধগম্য হচ্ছে না কিন্তু ক্রিকেটের আর উন্নতি হবে না এরকম বাংলা দেশি হাজারো মানুষ আছে যারা ক্রিকেটের ভক্ত আমরা সাকিব ভক্ত রাজনীতি তোলপাড় করে দিল আমাদের মত হাজার হাজার সাকিবকে সমস্যা বাংলাদেশের আইসিসির না সমস্যা সারাবিশ্বের বাংলাদেশের আমরা একটা গর্বের মানুষকে হারালাম দুঃখে আমরা শোকাহত তবে আর কিছুই বলার নাই তবে একটা কথাই বলব সাকিব তুমি ভালো থেকো সুখে থাকো,0,sports
বিসিবির সভাপতি বদলা আবাল মার্কা বিসিবি নিজের দেশের জন্য শেষ করে ফেল,0,sports
এগুলা ইন্ডিয়ার চাইল,0,sports
আমরা সাধারণ দর্শক আমারা এত কিছু বুঝিনা আমরা চাই সাকিবরা আবারও মাঠে ফিরুক।,0,sports
কাপ কারা নিবে।?? রাজশাহী নিবে,0,sports
আবারও ম্যাচে অ্যাম্পিয়ারের আরো একটি ভুলের কারণে হারলো। রাইলি রুশোর কে অ্যাম্পিয়ার অস্বীকার করল। পরে দেখা গেল ওই টা হয়েছে। টা যদি অ্যাম্পিয়ার দিত। তাহলে হয়তো জিততে পারতো। 👈👈👈,0,sports
চামচামির একটা লিমিট আছে। সাইড এর জারসি পরাটার লাফালাফি দেখলে হালার বিচি টা কাটে নেওয়ার ইচ্ছা হয়।শালা ফকিন্নি রবির বাচ্চা।তেলবাজি কর টাকা নেওয়ার ধান্দা।,0,sports
একাই বহুরূপী মানুষ আগে কি বলল এখন কি বলে,0,sports
হয়তোবা ভূল বুঝাবুঝি হয়েছে,0,sports
মতামত পাপনের বিরুদ্ধে।তাহলে পদ তেগ করেনা কেনো?,0,sports
আফিফের ক্যাচটা সেরা হয়ছে।,0,sports
যে দুইজন ভিতরে নিয়ে গেল ওরা কোন প্রকার ধান্দা করলে মিডিয়াকে জানান,0,sports
মানুষ পাগল হয়ে গেছে।এখানে পাপনের কি দোষ।অন্যায় করছে সাকিবেশাস্তি দিচ্ছে আইসিসি।টাকার জন্য পাগল হয়ে গেছেখেলা চেরে সব খেলোয়ার টাকার পিছু ছুটছে।আমি তো বলবোসিনিয়ার খেলোয়ারদের টাকার হিসাব নেয়া হক।পাপন স্যার ক্রিকেট বোর্ডের জন্য ঠিক আছে।এদের ঠাইট রাখার দরকার আছে।,0,sports
ভাই ঐ বিকৃত মস্তিষ্কের সাংবাদিক রা প্রেস কনফারেন্সে এইটা নিয়ে জিজ্ঞেস না করলেই হতো।<br />আরো অনেক কথা জিজ্ঞেস করার মত আছে। বিরাট কোহলিকে কি তারা চেনে না? আমার এই একটা কুয়েশ্চেন ভাই আপনার কাছে :),0,sports
পাপন দাদা কে কোচ বানানো হোকপ্লান ঠিক নাই খেলার😂😂😂😂,0,sports
অভিনন্দন দুই দলকে দুই দলেই অনেক ভালো খেলেছে বন্ধুরা স্বপ্ন ছিল খেলোয়াড় হইবো কিন্তু হতে পারি নাই তাই ইউটিউবে একটা আপনাদের সাবস্ক্রাইব করার অনুরোধ রইল সবাই অবশ্যই আমার চ্যানেলটি সাবস্ক্রাইব করবেন ইনশাআল্লাহ,0,sports
পাপন সাহেবের এখানে বলা উচিত ছিল যেযারা দলে বা ঘরোয়া ক্রিকেটে ভাল পারফরমেন্স করবে তাদের বেতন বোনাস সব ঠিক হারেই বাড়ানো হবেযারা এক ম্যাচ খেলবে আর ম্যাচ রান করে সাজ ঘরে ফিরে যায় এরা কিভাবে বেতন বাড়ানোর কথা বলে!!!লাখ লাখ টাকা বেতনেও যদি এদের না হয় তবে দেশের হয়ে না খেলাই ভাল এই দেশের ক্রিকেটে!!!,0,sports
কে কে পাপনের পদত্যাগ চান??,0,sports
এজন্য তুমি তাসকিন ভাই জাতীয় টিম এর জগ্য না।।।।। ফালতু তুমি।।।।।,0,sports
"ভাইয়া আপনার কথাগুলো অনেক ভাল লেগেছে।আমরা আসলে আমাদের নিজেদেরকেই দিন দিন অনেক ছোট করছি!ভালো থাকুক সাব্বির রহমান,ভালো থাকুক আমাদের ক্রিকেট।<br />আপনার জন্য ও শুভকামনা ভাইয়া।",0,sports
ফাউল,0,sports
তাদের যে বেতন বাংলাদেশ হিসেবে অনেক বেশি দেশের মাটি ছাড়া কোথায় এমন কি এনে দিয়েছে,0,sports
দশ বছরে কোন বাল ফেলাইছ,0,sports
মুশরিক ক্রিকেটার হয়ে কি হয়ে গেছে বাংলাদেশের। লোকটা বলতাছে ও কিছু বলেনি তারপরও তার সাথে কিরম ব্যবহার করে। ইন্ডিয়ান ক্রিকেটাররা যদি হারে তাহলে ইন্ডিয়ার লোকেরা যে ব্যবহার করে এগুলা যদি ওদের সাথে করা হতো তাহলে কি জানো করতো ওরা।,0,sports
বস মানে মাশরাফি,0,sports
বাইঞ্চোদ মার্কা একটা লোক।এগুলোকে বাদ দেওয়া উচিৎ।,0,sports
বিসিবির সভাপতি অবশ্য দায়ী।সেই প্রতিশোধ নিতে চাচ্ছে সাকিবের উপর অথচ পুরো দলের ক্ষতি হয়ে যাচ্ছে,0,sports
পাগল হয়ছে,0,sports
গালাগালি করছে তো কি বাল ফালানি গেছে,0,sports
খুব খুব খুব মিস করব সাকিব ভাই আপনাকে,0,sports
অনেক খারাপ লাগে ভাইয়ার জন্য।,0,sports
আল্লা আশরাফুলের মত যেন কিছু না হয়। ষড়যন্ত্রকারির মুখোশ উন্মোচন চাই।,0,sports
শেষের মুহুতটা দেখার মতন,0,sports
সাকিব ছাড়া বাকীদের বাল ছিড়তে নেওয়া হয়েছে?? সাকিব উইকেট রান করেছে। এটা কি খারাপ পারফরম্যান্স,0,sports
"এগুলা কেন দেয়,এতদিনে??<br />👿👿👿😎😎😎😎",0,sports
গালি দিতে পারছিনা কিন্তু কিছু না বলে পারছিনা । বার বার ইন্ডিয়া না বলে সেই ব্যাক্তিকে খারাপ বললে সেটা খুব একটা মন্দ হতো না। কারণ জুয়াড়ি দের মতো ব্যাক্তি কোনো দেশ জাতি ধর্ম বর্ণ দেখেনা এরা মানুষের শত্রু । ভারতের অনেক খেলোয়াড় জুয়ারিতে ফেসেছে । সাকিব আমারও একজন অতি প্রিয় খেলোয়াড় তবে ও বোর্ড কে জানাতে পারতো তাহলে তো ওই জুয়াড়ি ব্যক্তি ফেঁসে যেত কিন্তু কিছু মুর্খ জনগণ বলছে সাকিব কে ফাঁসানো হয়েছে । যদি ফাঁসিয়ে থাকে সেটা আপনাদের দেশের লোকই ফসিয়েছে ।,0,sports
জুয়ারি পাপ,0,sports
রুবেল সৈই চালাক । মেয়েটি লোভী ছিল । উল্টা ঠকছে।শেষে রুবেল কেটে পড়ছে,0,sports
সাব্বির কে দলে চায়,0,sports
বাংলাদেশের নতুন হিটার🔥🔥🔥 ঃ আফিফ হোসাইন ঃ মোহাম্মদ নাঈম ঃ মেহেদী হাসান ঃ হাসান মাহমুদ্ ঃ মেহেদী হাসান রানা জাস্ট ওয়াও🔥🔥🔥🔥আগামীর বাংলাদেশের ভবিষ্যত প্রজন্ম,0,sports
হুম,0,sports
"<a href=""https://www.youtube.com/watch?v=j7jgM0yFBL4&amp;t=1m44s"">1:44</a> সাব্বির রহমানের মোবাইল নাম্বার জাতিরে না দেখালেও পারতেন। জাতি তো তারে এখন শান্তিতে ঘুমাইতেই দিবে না :D",0,sports
আশফুল কে ইমরুল কাইস কে চাই সবাই বলন,0,sports
পাপন যদি না থাকেতাহলে উন্নতি সম্ভব৷,0,sports
!,0,sports
পাপন একটা বেয়াদব,0,sports
খেলা দেখা বন্দ,0,sports
এগুলা সব পাপনের চাল আন্দোলন করাতে ওর উপর প্রতিশোধ নিয়েছে,0,sports
পাপনের পদত্যাগ দাবি জানাচ্ছি।কিছু দিন আগে সফরে সুজন সাহেব যে ক্যাসিনোতে জোয়া খেলেছে তার কি বিচার করেছে ।বিসিবি কে তীব্র নিন্দা জানাই ।,0,sports
সাকিবুল হাসান কে দল থেকে বঞ্চিত করা মানে বাংলাদেশের দলটাকে ধ্বংস করা,0,sports
পাপনের পদত্যাগ চাই আজকের পর থেকে যতোদিন পর্যন্ত শাকিব আবার মাঠে না খেলবে ততদিন পর্যন্ত ক্রিকেট খেলা দেখবো না সাকিবের যায়গায় পাপন মামা খেলবে তাই সাকিব কে বহিষ্কার করেছে পাপনেরে সামনে পেলে মনের সাদ মতো জুতাপিটা করতাম।😈😈👿👿,0,sports
কোনো দরশক গালি দিতে গ্যলারিতে যায়না মনে হয় কারো ভুল হচ্ছে।,0,sports
মুরফিক কিছু কোনো টেনশন নাই দালাল গুলে এত টেনশন কেন,0,sports
এতদিন ম্যাচফ্রিকিং করছে পাপনকে সাথেনিয়ে । এখন পাপনের গায়েবেজেছে তাই ফাসিয়েছে পাপন । বছরের সাস্তি । সবাই চোর । এটা আরো আগে উচিত ছিল। সাকিবতো মাঠে সোনা ধরে দেখাইলো এখন চোরের মতো দারিয়ে আছে কেন এখন সোনা দেখায়না কেন । পাপনের সাথে মিলে ভারতের টাকা খেয়ে দেশকে অনেক ঠকিয়েছে ।,0,sports
অনেক অনেক ভালো,0,sports
সিলেট তার প্রথম জয় অসাধারণ ভাবে পেয়েছে। এগিয়ে যাও সিলেট। আমাদের দোয়া রইলো । এবারের বিপিএলে সিলেট জিতবে ইনশাআল্লাহ।,0,sports
পাপন সাহেব জাতি তোমাকে ক্ষমা করবে নাতুমি যা করতাছো চিন্তা ভাবনা কইরা কইরোসাকিব বিহীন বাংলাদেশ টিম একটি মেরুদণ্ডহীন প্রানির মত।বাংলাদেশ ক্রিকেট টীমের জন্য তোমার কোন বালের অবদান ও নাই!তুই মানুষ হ পাপনতুই মানুষ হ!,0,sports
অারে বোল্ড কর বোল্ড,0,sports
ভাই সানি লিওনি কে পছন্দ করেন না।।।,0,sports
বাংলাদেশী প্লেয়ারদের শরীরে তেল জমছে,0,sports
বলদ,0,sports
তাদের কে পাগলের উপাধি দেওয়া হক যারা রাজি আছেন তারা হ্যা বলুন,0,sports
সব বলদ এসে একগাদা হইছে 😑,0,sports
হারে এদের কে দলে রাখবার কোন দরকার নাই দল থেকে বাদ দেওয়া হোক,0,sports
ছেলেটা দুস নাই জে মারতে গেছে তার দুস,0,sports
সারা পৃথিবীতে আমাদের 🇮🇳🇮🇳 গান ছাড়া আনন্দ জমে না এটা👆 প্রমাণিত 😄😄😄😄😍😍,0,sports
পাপনকে সরাতে হবে,0,sports
সবাই প্লিজ এই ভিডিওটা দেখেন পাপন বাংলাদেশ ক্রিকেটের টাকা নিয়ে জুয়া খেলতেছে,0,sports
প্লাটুন😍😍😍,0,sports
হতুপজডরসআএ৭পনটীচজে০িগএতসীুম,0,sports
সাব্বির সেরা,0,sports
এই এক বছরে বিশ্ব সেরা টা পাপনের বাপ পাবে। সাকিবের ধারাবাহিকতার জন্য ভারতের মালুরা বিশ্বসেরা অল রাউন্ডের হতে পারছেনা সেই জন্য বছরের জন্য নিষিদ্ধ করে সাকিবকে দামিয়ে রাখা হলো মালুদের বিশ্ব সেরা বানানোর জন্য কারও বুঝতে সমস্যা হলে আজকের তারিখটা লিখে রাখুন আগামী এক বছর পরে যদি সাকিব ফিরেও আসে তখন বিশ্ব সেরা অলরাউন্ডার হয়ে যাবে ভারতের কোন এক মালুর বাচ্চা শুধু এটার জন্য এক বছর সাকিবের স্কোর শূণ্য করে দিলো মিলে যাবে। পাকিস্তানের অনেক খেলোয়াড়ের জীবন এভাবে ধংস করা হয়েছে আইসিসি নামক ভরতীয় দালাল চক্র দ্বারা। আর ভারতের সাথে সিরিজটা দল ঘোষনা করলো আইসিসি নামক ভারতের দালালরা। সবকিছু ভারতের চাল আর আমরা তাদের পা চাটা গোলাম হিসাবে সবকিছু গ্রহণ করে নিলাম আমাদের উচিৎ ছিলো ভারতের সাথে সিরিজটা বর্জন করা এবং আইসিসির মন গড়া রায়ে প্রতিবাদ করা। আমি ছোট বেলা থেকে ক্রিকেট পছন্দ করি কিন্তু যখন বুঝতে পারলাম ক্রিকেটের সবচেয়ে বড় নিয়ন্ত্রণ সংস্থান ভারতের মালুদের দিয়ে নিয়ন্ত্রীত হয় তখন ধিরে ধিরে ক্রিকেটকে মুছে ফেলতে শুরু করলাম বাকি ছিলো দেশের ছেলেদের সমার্থনের বিষয়টা সেটাও আজ হারিয়ে গেলো। দিয়ে সারা পৃথিবীর সেরাদের দেশে এনে তাদের দুর্বলতা গুলো খুজে নোট করে রাখে পরে কাজে লাগানোর জন্য দিয়ে তারা বিশ্ব ক্রিকেটের নিয়ন্ত্রণ নিয়েছে আর তার জন্য ভারতকে আজীবনের জন্য ক্রিকেট থেকে নিষিদ্ধ করার দরকার ছিলো আইসিসি নামক দালাল চক্রের এটা আমার মনে হয়েছে তবে হয়তো ভূল হতে পারে আমার কারন আমি এতোটা শিক্ষিত মানুষ না। আজ একটা জিনিস ক্লিয়ার ভারত নিয়ন্ত্রিত কোন বিষয়বস্তু নিয়ে আমাদের সরকার প্রতিবাদ করতে পারবেনা সেটা যুদ্ধ হোক আর খেলার মাঠ।৷ আমার কথা ভালো লাগলে আমার চ্যনেলটা সাবস্ক্রাইব করবেন এবং কমেন্টে একটা লাইক দিয়ে যাবেন। ধন্যবাদ সবাইকে।,0,sports
হাইলাইট দিন,0,sports
দূর সালা ভুয়া,0,sports
মুশফিককে গালি দেওয়ার অপরাধে একটা ছেলেকে সবাই মিলে রাগিং করতাছে কিন্তু এরচেয়েও বেশিভয়ঙ্কর গালিগালাজ হুজুরে পাক সাল্লাল্লাহু আলাইহি ওয়াসাল্লামকে করেছেন কিন্তু তার উত্তরে কয়েকটা হুজুর শহীদ হয়েছেন কি আজব দেশ,0,sports
আরে ভাই গালি দিয়েছে তা এতো কি হয়েছে ।,0,sports
সালার বাংলাদেশ নবী করীম সাল্লাল্লাহু আলাইহি ওয়াসাল্লাম কে গালি দেয় বিচার নাই আজ একজন খেলোয়াড় কে গালি দেয় নি অথচ কি আশ্চর্য আহ,0,sports
রুবেল একটা ফালতু বাড বাংলা দেশের খেলোয়ারা ফালতু রুবেল তোর চেহারা অনায় দেখ হ্যাপি তোর চেয়া দেখতে অনেক ভালো,0,sports
সাব্বিরের সমালচনা করেছেন জাহারা তাহাদের লজ্জা থাকা উচিৎ ছিলো<br />তাহারা দলের জন্য কিছুই করতে পারেন নাই,0,sports
কিশোরগঞ্জের মানুষ ঘুষ খাইনা।,0,sports
ক্রিকেটার দের আন্দোলনের পরেই এই ঘটনা হলো সুতরাং এইটা ইস্পষ্ট যে বিষয়টা আইসিসিকে বোর্ড সভাপতি জানিয়েছে।,0,sports
সাকিব কে মিডিয়ার সামনে আনলে সব বের হয়ে যাবে সব পাপনের কারসাজি,0,sports
খুব খারাপ লাগছে আমার একটা পছন্দের খেলোয়াড় ছিল।,0,sports
"খুশি মানে এতটাই খুশি, বাংলাওয়াস খাইছি কোন দুঃখ নেই,,,",0,sports
হাসুআপার চাল,0,sports
তারে পিটানের। দরকার। বেশি বেয়দপ। ওকে জরিমানা করা হক। দলতে কে বাদ। দাওয়া হক। বালো ঘোলোয়ার। আচে ওদের। কে টােকান,0,sports
পাপী পাপন ধংস করবে বাংলার গৌরবের ক্রিকেট। পাপন তারাও ক্রিকেট বাচাও 😠😠😠,0,sports
আমরা যখন লাইভে খেলা দেখি তখন দেখি এবং শুনি যে এই সব প্লেয়ারদের মানুষ কত গালি দেয়। তাছাড়া আমি তো বাংলাদেশি প্লেয়ারের খেলা দেখাই বন্ধ করে দিয়েছি। জীবনেও আর ফালতু পোলা পানের খেলা দেখবো না।,0,sports
গালি টা না দিয়েই বললাম তাহলে গালি বয় রানা ঘুষখোর এটা লেখা হল কেন।,0,sports
খারাপ খেল্লে কিছু ওল্টা পালটা বলতেই পারে পাবলিক তার জন্য এমন করতে হয় বাল মুশফিকেও ফালতুমি করলো,0,sports
আমার চ্যানেল থেকে ঘুরে আসুন ।ভিডিও গুলো দেখলে হয়তো ভালো লাগবে এখনি এই লিংকে কিল্লিক করুন,0,sports
সাকিব আল হাসানের বদলি হিসেবে পাপন আল হাসান সফরে যাচ্ছেন,0,sports
আমি যতদিন আছি সুযোগ নাই😁😁😁,0,sports
মেহেদী হাসান কে জাতীয় দলের অন ডাওন ম্যান হিসেবে দেখতে চাই আফিফ কে ও দোলে চাই,0,sports
তাসকিন ভাই এটা কোনো প্রতিযোগিতা না মারামারি,0,sports
"তোরা সবাই মাদারচুদ
",0,sports
বাংলাদেশ একটি ছোটোদেশ।অর্থও কম।সেখান থেকে আমরা ক্রিকেটারদের জন্য যা করি তাকেউ করতোনা।বাট ক্রিকেটাররা আমাদের তেমন কোনো খেলা উপহার দিতে পারে নাই।অনেক গুলো প্রতিভা নিয়ে জাতীয় দলে চান্স পাওয়ার পর মাসের বেশি কারো প্রতিভা থাকেনা,0,sports
অবশেষে বাংলাদেশ ক্রিকেট ও রাজনীতির শিকার!!!!!,0,sports
আবগান এর লগে খেলার জনো এতো চিনতা কইরা উকেট বানানো লাগে তাহলে বছোর কার বাল ফালাইছো তোমরা,0,sports
মাথা নসট,0,sports
ঐটা তার সাতে ঠিক হয়নাই,0,sports
নাজমুল হাসান শান্তর বাদ চাই,0,sports
জাতীয় দলের ক্রিকেটার এর বিরুদ্ধ হয়ে এরকম বাজে রিপোর্ট শুধু এদেশের সাংঘাতিক রাই করতে পারে।,0,sports
ও খেলা দেখতে গেছে গালি দিব কেন।,0,sports
বাংলাদেশের ক্রিকেট ধংশ হয়ে যাক। নিপাত যাক।,0,sports
সবাই দেখছি বলছেন মাহামুদুল্লাহর জন্য খারাপ লাগচ্ছে আশ্চর্যকথা পুরুটা টুর্নামেন্ট ইমরুল দারুন ভাবে ভালো ডোমিনেট করলো আর এখন সকল ক্রেডিট নাকি মাহামুদুল্লার!!!,0,sports
ভাই রাজনীতি এর নাম রাজনীতি আমাদের মাঠগাট নদীবন্দর সব কিছু খেয়ে ফেলছে রাজনীতি,0,sports
সাবাস বেটা খেলা হইছে,0,sports
আফিফ হোসেন খুব ব্যাট ও বল হাতে খুব ভালো। সৌম্য সরকার এর অনেক দিন পরে বেশি রান করেছে নিয়মিত ভালো রান পাই যে বল হাতে অনেক ভালো করতেছে।,0,sports
এবার সবচেয়ে বড় ভুল হয়েছে ঢাকা বিভাগের সব পাকিস্তানি সব খেলোয়াড় নিছে ওয়েস্ট ইন্ডিজ এর খেলোয়াড় নেই নি পাকিস্তানি রা তো দেশী খেলোয়াড়ের চেয়ে অধম,0,sports
চট্রগ্রামের ভক্ত গুলা কই হাত তোলো,0,sports
এবার ফাইনাল খেলবে দুই ভায়রা আমার সাথে কে একমত আছেন লাইক কমেন্টস করুন,0,sports
রাজশহী সেরা,0,sports
"ক্রিকেটার হিসেবে ১০০ তে ১০০...,এই প্রথম এমন ক্রিকেটার দেখলাম।",0,sports
এটা ভারতের একটা ষড়যন্ত্র,0,sports
বাংলাদেশে এখন কি হয় তা কি জনগ বোজেনা,0,sports
"মোবাইলে কি গেমস নাই, গেমস খেল। মানুষের মন নিয়ে খেলা করিসনা,মৃত্যু সবার আছে, এগুলো করে বংশের পরিচয় দেছ। প্রেম করবা গোপনে সার্থ আদায় না হলে ছেড়ে দেবা অনলাইনে হায়রে জাতি।",0,sports
জত্তসব ফালতু,0,sports
আমরা পাপনের বিচার চাই,0,sports
হায়রে আবুল বাঙ্গালী এক লোকে কি কইছে না কইছে এল কেরে ধইরা এভাবে মারার চেষ্টা করতে পারি বাংলাদেশে যে কত মারামারি হয়েছে সেগুলোর কোন বিচার নাই আজাইরা নেতাগিরি,0,sports
সাবাস,0,sports
আসহাই কাকে বলে হেপিকে দেখলে ভুজা জাই,0,sports
পাপন হলো একজন চুর,0,sports
ধন্যবাদ মুজিবুর রহমানকে,0,sports
এবারের বিপিএল এ দর্শক নাই কেনো?,0,sports
কে সুপার ওভার এ খােলাতে হতো,0,sports
দর্শক অনেক কথা বলতেই পারে। এটাও দর্শকের একধরনের ভালোবাসা। এটা করা ঠিক হয়নি।দর্শক না থাকলে মুশফিকের পেটে ভাত ও জুটতো না। এতো অহংকার ভালো না। এ অহংকার বেশি দিন থাকবে না।,0,sports
পাপন কেছিনর মেইন গড ফাদার ওকে রিমাইন্ড দিলে সথ্তটা বলবে এখন কি বাব দেখাইতেছে,0,sports
রকিবুল ভাই এর সাথে কে কথা বলছে,0,sports
কমেন্ট টা পড়বেন কিনা জানিনা ভায়া।তারপরেও বলিআপনার কথাগুলো একদমই ফেসবুকের আম জনতা পাব্লিক এর মতো লাগলো। হ্যাআপনি ক্রিকেট বিশ্লেষক না কিন্ত তারপরেও কোনো বিষয় নিয়ে ভিডিও বানাতে হলে একাটু ঘাটাঘাটি দরকার। আমজনতা তো আর খবরের ভেতরটা জানেন না কিন্তু যারা জানেন তাদের কাছে আপনার এই কথাগুলা খুবই লেইম। আশাহত আপনার এই।ভিডিও দেখে। বিষয়গুলো ক্লিয়ার করলাম না।,0,sports
"ওর সেলিব্রেশেনে আমি অনেক অনেক খুশি,,,,,,,",0,sports
পাপনকে জুতা দিয়া এমন ভাবে পিটান।সালা ভারতের দালাল।,0,sports
সাকিব ভাইয়ের জন্য কষ্ট হচ্ছে সাকিব ছাড়া বাংলার ক্রিকেট কল্পনা করা যায় না !,0,sports
আমি হলে জুতা মারতাম সব কয়টাকে,0,sports
এমন ঠিক না,0,sports
আশরাফুল যদি তখন থাকত তাহলে আজ উন্নত হতো।পাপন কান্না করাইলি।খোদার কসম যদি তোকে পাইতাম তাহলে তোকে জুতা দিয়ে পিটাইতাম,0,sports
সাকিব এই দেশকে সব দিয়েছে কিন্তু এই দেশ সাকিব কে কিছু ই দিবেনা। সাকিব এখন তুমি তোমার নিজের জন্য কিছু কর।,0,sports
মেহেদি হাসান খুব ভাল ব্যাট করেছে,0,sports
তথ্য প্রযুক্তিবিদ সালাউদ্দিন সেলিম তার ফেসবুকে লিখেছেন ;নিজের ঘরের ফোন রেকর্ড কীভাবে আইসিসির হাতে যায়? এ সামান্য ব্যাপার যদি পাপন ওভারকাম করতে না পারেন তাহলে এমন অযোগ্য মূর্খ লোক বিসিবিতে থাকার প্রয়োজন নেই;,0,sports
ভাই আমি আপনার সাথে এক মত,0,sports
বিশ্বাস করেন রাসেল ভাই এটা দেখার জন্য মুটেও প্রস্তুত ছিলাম না 🙃,0,sports
একজন পাপন চলে গেলে ক্রিকেট এর কোন ক্ষতি হবে না কিন্তু একজন সাকিব চলে গেলে অনক ক্ষতি হয়ে যাবে,0,sports
পাপন সাহেবের পলিটিক্সের পল্টিবাজীর একটা অংশ সাকিব আল হাসান অলরাউন্ডার,0,sports
সাকিব তো বলল যে খেলার আগেই জানা যেত যে কে হারবে কে জিতবে এই সত্য কথা বলাই তার অপরাধ।,0,sports
❤️✊ 🌎 🏴󠁧󠁢󠁥󠁮󠁧󠁿 পাপন হঠাও দেশ বাঁচাও পাপন নয় ন ভাত দিলে কি খয় শুদু পাপ হয় সেটাই পাপ দা ?,0,sports
তোর সময় কত স্টেডিয়াম নস্ট হইছে খবর আছে।।।সালা বালপাকনা পলিটিশিয়ানদের মত ষড়যন্ত্র খুজিশ।,0,sports
সাব্বির এখন উইকেটে একটু সময় নিয়ে খেলে যেটা একটা ভালো দিক তাই ওর জন্য ওপেনিং পজিশন টাই ভালো।,0,sports
সৌম্যরে নিয়ে আর পারলাম না দুইবার ব্যাট করেও তার হয়না,0,sports
তামিম ইকবাল সেরা।,0,sports
যখন বেতন বারানোর কথা বলছে তখন দোষ ধরা শুরু হয়ে গেছে। সব রাজনীতি,0,sports
আসসালামু আলাইকুম। হ্যপি আপু আপনি মনের কষঠ ভুলে যান। কারন আললাহ যা করেন ভালো করেন।এতে অসনতুষঠ হবার কিছু নাই। আপনি। আললার উপর ভরসা রখুন।,0,sports
পাপনের কারণে সাকিব আল হাসানের ক্যারিয়ার নষ্ট হতে দেয়া যাবে না,0,sports
ইনশাআল্লাহ সাকিব আবার ফিরবে,0,sports
নাইম অনেকটাই সাকিবের মত ব্যাটিং করে,0,sports
পাপন জুয়াড়ি,0,sports
সাকিব আল হাসান এর মধ্যে একটা হতাশা আর ভয়ে দেখা যাচ্ছে এটা এর মধ্যে একটি চক্রান্ত,0,sports
বোর্ডের সাথে ক্রিকেটারদের দুরত্ব সম্পূর্ণ ভাবে বোঝা যাচ্ছে। আল্লাহ না করুনদেশের ক্রিকেটে বড় ধরনের ঝড় আসতে চলেছে,0,sports
সময় news এটাত আগেও দেখছি পরান news .বালের নিউজ,0,sports
সাকিব হলোমিসিবির আবরার ফাহাদে,0,sports
অনেক কষ্ট পাইছি আজ ।আর পাপন সাব আমি জানি আমার কমেন্টস আপনার চোখে পরবে না । কিন্তু আমার দুঃখ আপনি কোচ নিয়োগ এত ভাল তাহলে পেস বলার ছারা কেন খেলতে নামল ।আর আপনি সাকিবেরে এই বাইনচুদেরে কেন অধিনায়ক বানাইলেন। আমি আপনারার চাইতে খেলা কম বুজি না আমি বলে দিচ্ছি এই সাকিব অধিনায়ক থাখলে দেশের ক্রিকেট ধংশ হয়ে জাবে ।জারা এই লেখা টা পরবেন স্ক্রিন সট দিয়ে রাখেন বলে দিলাম। সিনিয়রদের সাথে সাকিবের সম্পক ভাল না দেখতেছেন সবাই তার পর ও কিছু করতেছেন না । আমি গেরানটি দিয়ে বললাম বড় রা সবাই ইচ্ছে করে খারাপ খেলছে।।।,0,sports
সব মোহ এবং ্ভণডামি,0,sports
দু একটা পাডা আতালে লাগে,0,sports
বাল দিসো হাইলাইডসের মাঝে বার বাউন্ডারি দেখানো লাগে,0,sports
পাপনদা অাপনাকে কেউ চায়না এটাই অাপনে বুললেন না।,0,sports
ভাই আপনার কথা গুলো খুব ভালো লাগে<br />আপনার কাছে একটা চাওয়া আছে ভাই,0,sports
পাপন সহভারতেরদালাল,0,sports
আশাকরি দেশের সবাই ভাল করুক,0,sports
একটু আকটু হবে 😂🤣😭,0,sports
অসাধারণ মুসফিকুর রহীম,0,sports
পাপন এর পাপে বাংলাদেশর ক্রিকেট শেষ,0,sports
ভোদার সেন ওয়াটসন নিছে রংপুর,0,sports
এটা তো মনে হলো নাছির সুবা,0,sports
চিন্তা করবেননামাস পর পাপন বলবে সাকিব এখন আর জাতীয় দলে খেলার জন্য ফিট না!!!!!!!!!!!!!!!!!!!!!!!!,0,sports
আমাদের দেশের ক্রিকেটারদের জন্য এটা খুব লজ্জার বিষয় যে তারা সুপার স্টার হয়ে গেলে তাদের অতীত খুব সহজেই ভুলে যায়,0,sports
এলিমিনেটর দেখা হোক।ঢাকাকে খেয়ে ছেড়ে দেয়া হবে,0,sports
উপরে বন্ধুদেশ বলে ।আর আড়ালে অপেক্ষাই থাকে ক্ষতিসাধন করতে।মুত্র পানকারী ছাড়া আর কেউ না এই ষড়যন্ত্রের।না বুজলে মুড়ি খান।,0,sports
বাংলদেশে কিছো কিছো জানুয়ার আছে যার কারনে বাংলাদেশ এিকেট টিমটা সেশ হয়ে যাবে যতসব ভালো খেলুয়ার আছে এক এক করে সবাইকে কনুনা কনু দুসারপ করে বাংলাদেশ দলটারে সেশ করে দিতেছে,0,sports
পাপনের বাবাতো অনেক ভাল ছিলেন।পাপন সালা এত কারাপ কেন।এখনও সময় আছে পাপন ভাল হয়ে যা,0,sports
হটাও পাপনবাচাও ক্রিকেট,0,sports
সবাইকে সালের অগ্রিম শুভেচ্ছা। কারা কাপ নিতে পারে এবার??,0,sports
পাপন হঠাও ক্রিকেট বাচাও ক্রিকেট বক্তরা,0,sports
আসলে রুবেল বাজে ছেলে মেয়েটা সটিক বিচার পাইনি,0,sports
জারা অননাই করেছে তাদের শাস্তি হোক সাকিব তো নির্দোষ তাকে কেন শাস্তি দেওয়া হল,0,sports
রুবেল ও হ্যাপির রে তুই অপরাধী রে,0,sports
ধুর পাগল হয়ছ নাকি ব্যাথা পায়ছে,0,sports
পুটকি মারো সাব্বিরকে গুরা দিয়ে সালা বরি খোর,0,sports
খারাপ সময় কাকে বলে বুঝবে এখন সাব্বির......,0,sports
আঙ্গুল ফুলে কলাগাছ পাপনের অবৈধ সম্পদের হিসাব নেওয়া হোক,0,sports
কান্না যে কিছুতেই থামাতে পারছিনা ভাই সবই আছে আমার জীবনে কিন্তু ঐদিন টা থেকে জীবন থেকে যেন কি হারিয়ে গেল ‌।,0,sports
আমি জতদিন আছি সুজগ নাই,0,sports
ভাই সকিব বলে ছিল মাঠে নামার আগে সিদ্ধান্ত হয়ে যায় এটা নিয়ে কেও প্রশ্নের মুখমুখি আনেনি পাপনকে সব পাপনের খমতার অপব্যেবহার করতাছে????,0,sports
এই টা কনো প্রতি যোগিতা হল বালের প্রতি যোগিতা আর প্রতি যোগিতা ছিলনা মেজায টাই খারাপ কইরা দিছে আর জিবনেও তদের ভিডিও দেকবো না,0,sports
পুরাই বাঙালি,0,sports
ফজলে মাহমুদ কে জাতীয় দলে চান্স দিয়া উচিত সামনের সিরিজ এ আশা করি রানা জাতীয় দলে চান্স পাবে,0,sports
আমার মনে হয় চট্টগ্রামের কোচ জনি জিন্সের মেলায় হারিয়ে যাওয়া জমজ ভাই আপনারা কি বলেন?,0,sports
এই সব মারা মারি করা বাজি এই সব ঠিক না ফালতু,0,sports
বাংলাদেশের প্রাণ সাকিব আল হাসান ফিরবে আবার বীরের বেশে ইনশাআল্লাহ😍😍😍🇧🇩🇧🇩🇧🇩,0,sports
মাশরাফি গ্রেগরির নামে মামলা করে দিবে😄,0,sports
সাকিব কে দিয়ে ক্ষমা চাওয়ানো হলো কেন? ওতো জুয়ারিদের সাথে আঁতাত করেনি । অপরাধ করল জুয়ারিরা তাদেরকে ধরেনা অথচ শাস্তি পেল শাকিব।🔥🔥🔥🔥🔥,0,sports
"গন্জিকা একটু কম সেবন করো ভাই, আর নিজেকে কখনও সিলিব্রিটি ভাবতে নাই",0,sports
ছেলেটাকে এইভাবে হেরেস করারতো কিছু নেই চামচার বাচ্চা যত সব,0,sports
এমনি ভালো লাগে না তার পর আবার সাকিব নাই।পাপন মিয়া কে দেখার জন্য কি আর খেলা দেখবো।চুর বাড়ি গেলে যে গিরস্থের সাজা হয়।আজকে জানলামঅনেক সমস্যা থাকতে পারে জেই কারনে হয়ত বলে নাই।,0,sports
মিস ইউ বস সাকিব আল হাসান😍🌺💜,0,sports
সাব্বির ভাই কে আমি খুব মিস করি সে আমি আর আল্লাহ ছাড়া কেউ জানেনা,0,sports
লোকটার কথায় বুজা যায়। লোকটা ভদ্রলোক।,0,sports
তাদের জাতীয় দলে খেলার যোগ্যতা নেই।,0,sports
বিসিবি থেকে পাপন কে বহিস কার করা হোক তাহলে সব ঠিক হবে,0,sports
ওরে আজীব নিষিদ্ধ করা হোক,0,sports
সাকিবের নিষেধাজ্ঞা এক বছরদেখতে দেখতে যাবে। পাপনের চক্রান্তপাপনর পদত্যাগ চিরদিনের জন্য চাই,0,sports
পাপন সাকিবের সাথে ষড়যন্ত্র করে নাইকরেছে সকল ক্রিকেট প্রেমির সাথে। পাপনকে ঐই পদ থেক গাড় ধাক্কা দিয়ে বের করে দেওয়া হোক।,0,sports
সাবস্ক্রাইব করলে সাবস্ক্রাইব করমো,0,sports
মুশফিকরে গালি দিলে হইছে কোন বাল ও কোন বাল ওর চাইতে বড় বড় মানুষকে গোয়া মাইরা উপুর কইরা রাখে আজকালকার মানুষ,0,sports
নাসির ও রুবেল তোদের নরকেও জায়গা হবে না,0,sports
এবার ঠেলা সামলা পাপন সাহেব শালা তুই সব লুটেপুটে খাচ্ছে তাহলে কইয়া দিমু,0,sports
আজ যদি তুমি রুখে দাড়াওকাল তুমি শেষ 😭 হ্যাঁ এটাই বাংলাদেশ 🇧🇩,0,sports
মনে হচ্ছে গভীর কোন ষড়যন্ত্র। ভারতের ইন্ধন থাকলে তো থাকতেও পারে কারন ভারত চায়বে না বাংলাদেশ ক্রিকেটে ভারতের চেয়ে এগিয়ে যাক।,0,sports
সাকিব ছাড়া বাংলাদেশ ক্রিকেট দল অচল এটা ঠিক না। চলবে দল গরু দিয়ে হাল চাষ না দিয়ে ছাগল দিয়ে হাল চাষ করার মত। সাবিক এর কাছ থেকে এদেশের নবাগত ক্রিকেটারদের অনেক কিছু শেখার এবং জানার আছে। সাবিক একটা নাম না একটা ভূবন যা আমাদের জন্য সৃষ্টিকতা দান। বোড চেয়ারম্যান যে কেউ হতে পারে কিন্তু সাকিব হওয়া যায় না। আমাদের মনে রাখা উচিৎ।,0,sports
বাংলাদেশ জাতীয় cricket দলে কিছু বেয়াদ্দপ আছে তাদেরকে জাতীয় দল থেকে বের করে দিয়ে অন্যদেরকে সুযোগ করে দেওয়া হোক এই বেয়াদব দের জন্য দেশের এবং দলের ভাবমূর্তি নষ্ট হয়,0,sports
ঢাআআআআআকা,0,sports
তোর সম্পদের হিসাব বের করলেই সব কিছুর সমাধান হয়ে যাবে।,0,sports
বিসিবির উচিত নতুন কিছু আইন করাযেমন যেই ক্রিকেটার ম্যাচে কোন রান করতে না পারবে সেই মাচে ক্রিকেটারদের কোন ম্যাচ ফি দেওয়া হবে না।,0,sports
ফোন কল ট্যাক করেছে পাপন,0,sports
মুশফিকুর রহমানকে প্লেয়ার হিসাবে না তাকে তাঁর স্বভাব চরিত্রের জন্য সবচেয়ে বেশি ভাল লাগে। জাতীয় দলে আর জাতীয় দলের বাইরেও তিনি একজন উত্তম স্বভাবের লোক বলে মনে হয়।,0,sports
বাংলাদেশের একজন খেলোয়াড় কে গালি দেওয়া টিক না ওরা দেশের গর্ব,0,sports
সরকার আছে যতদিন ততদিন এসব দেখা ছাড়া কেনো গতি নেই। দেশটা রসাতলে ডুবে যাচ্ছে দিনে দিনে।,0,sports
কুত্তা কুত্তা পুলিশ সুপার হিরো আলম তাঁর কথা বলা হয় আর কোন বিকল্প ছিল এই সব কথা বলে যে এই যে কেউ না এই কথা তোদের সরম নাই আর এই কথা তোদের মাথায় নিয়ে কথা,0,sports
লজ্জা থাকলে পদত্যাগ করুন,0,sports
এই কথা দিয়া কোন বাল বুঝাইছেন??? আন্ডাযে চাপা মারার কি দরকার??? আপ্নারে চ্যানেল খুলতে দিছে কে??? মিয়া ফাইজলামি করেন কেন???,0,sports
কোটি টাকা কোটি টাকা।,0,sports
বালের বিপিএল একটা ম্যাচ ও দেখলাম না।।।,0,sports
আমি খুব বেশি খুশি হলাম,0,sports
বাংলাদেশের খেলা বন্ধ করে দেয়া হবে শাকিব ছাড়া খেলা হবে না মানুষ এত অন্যায় করে তাদের শাস্তি হয়না কেমন অন্যায় করেছে দুই বছরের জন্য বন্ধ হয়ে গেছে খেলা চলবে না বাংলাদেশের খেলা বন্ধ করুন,0,sports
সোম্য সট সিলেক শন ব্যাটিং স্টাইল সব আমার কাছে অনেক ভালো লাগে। সব চেয়ে বেশি ভালো লাগে যখন সামনে এগিয়ে এসে উড়িয়ে মারে সেটা ছয় হতে মিছ হয় না।,0,sports
পাপনসালাউদ্দিন বিসিবিবাফুফে কে খেয়ে দিচ্ছে 😑,0,sports
আজকের ম্যাচে যারা মানাব দ্যা ম্যাচ সেলেকশন করছে নাম্বারি করছে তা নাহলে সরকার ম্যাচ সেরা হবার কথা ছিলো।,0,sports
হায়রে কপাল এগুলো সব দাদাদের ইশারায় হচ্ছে,0,sports
প্লেয়াররা সবাই এমপি হতে চাইছে আসলকথা হচ্ছে রাজনৈতিক বীজ ঢুকছে খেলার মাঠে তাই এমনটাই হইতেছে,0,sports
আমি চিৎকার করিয়া কাঁদিতে চাইয়া করিতে পারিনি চিৎকারবাহ্ চুদির আই সি সি বাহ্,0,sports
সাব্বির আর সৌম্য সরকার দলে থাকবে তার এই অবস্থায় হবে,0,sports
চোখে পানি চলে আসলো!,0,sports
ভালোবাসার খুলনা ❤,0,sports
ধন্যবাদ মেহেদী হাসান রানা আমাদের গ্রামের নামটা উজ্জ্বল করার জন্য।দোয়া করি আরো এগিয়ে যাও।,0,sports
আমি এই ম্যাচে রাজশাহি কে সাপোর্ট করেছি কিন্তু ফাইনালে আমি খুলনা কে সাপোর্ট করবো😂,0,sports
ভাইরা এর দুশনেই এই শালা পাবনা কাল এসেছে আজ আবার যাবে,0,sports
আশরাফুল এর মতো সাকিব কে ও শেষে করে দিবে সালারা,0,sports
তাহমিদ ভাই এভাবে বলবেন না কান্না পায়! ভিতরের কথা গুলো নাড়া দিয়ে উঠেছে 😥,0,sports
এই পাপ্পনেই বাংলাদেশ ক্রিকেট কে ধংস করে ছারবে। যেমন টা করেছে আশরাফুলের বেলায় ঠিক তেমন্টাই হতে যাচ্ছে সাকিবের বেলা। সামনে অন্ধকার দেখতে ছে। জিম্বাবুয়ের মত করে ছারবে।এই পাপ্পনের পদত্যাগ করতে হবে,0,sports
মাশরাফি চদানির প,0,sports
"দোষ তার একার না,মেয়েরা আসে কেন? কয় মেয়েরা তো কোন সাধারন ছেলেদের কাছে যায় না। তার মানে একটা কিন্তু আছে! আর কি?",0,sports
সমস্যা কি এদের,0,sports
এখানে অপরাদি হচ্ছে পাপন সাকিব ভাই আন্দলন করাই সব কারন পাপনের পদতেক চাইসাকিব ভাই♥♥♥♥♥♥♥,0,sports
দালোলের বাচ্ছা গালি দিসে কার বাপের কি,0,sports
তার সম্পত্তির হিসাব নেয়া হক অতি ভক্তি চোরের লক্ষণ উনি আসার পর ক্রিকেটের অবকাঠামোগত উন্নয়ন হয়নি উনার কথাই সবাইকে মানতে হবে !!! কেন ?,0,sports
কি বললেন স্যার আমিতো জানি দেশটা আওয়ামী লীগের 😊,0,sports
বলদা রিপোর্ট,0,sports
পাপন বলেছেন সে চালায় না যদি চালাইতো তা হলে👻,0,sports
অদ্ভুত ভিডিও পেতে আমার চ্যানেল টি সাস্ক্রাইব করে রাখুন আপনাদের মন মতন ভিডিও দেওয়া হবে ইনসাআল্লাহ,0,sports
মিউজিকের মায়রে বাপ,0,sports
ইমরুল কায়েস কি বাদ নানুর শত্রু,0,sports
"এই টা দেখে নাকি আবার মেয়েরা পাগল হয়,",0,sports
ভূয়া পেঁচাল,0,sports
সাকিব এর কাছে এর মাফ চাইতে হবে,0,sports
সবগুলো পুরো পুরি পাগল সাথে তাসকিন ও পাগল হয়ে গেছে,0,sports
আরে ভাই সবকিছুতে সরি বললে চলবে না তাহলে আমি ধরে নাও একজনকে মারলাম নিয়ে বললাম সরি সেটা মেনে নেবে সেটা কেউ মানবে না তাহলে ওকে মারো না এমন মার দেওয়া যাতে দ্বিতীয় থেকে কোনদিন এভাবে গালি না দিতে পারে গালি দেওয়ার পর যা হয়েছে সরি বললে এটা কখনোই হয় না,0,sports
পাপন হটাওক্রিকেট বাঁচাও। ক্রিকেটে চোরের জায়গা নাই।,0,sports
প্রত্যেক শুক্রবার করে খেলা হইলে খুব ভালো হতো তাহলে অনেক দর্শক হতো,0,sports
চামচামি শুধু,0,sports
শাস্তি সব সময় আমাদের মতো দেশের জন্য ভারত বা বড় দেশের জন্য নয়,0,sports
অভিনন্দন রাজশাহী রয়েলসের জন্য শুধুমাত্র রাসেলের জন্য রাজশাহীর কাপ পেয়ে গেল।,0,sports
চারাল তোর বিচার হবে। তোর বংশের মুখে জুতা মারি আই সি সির সব চারাল ইন্ডিয়াদের ঘরে ঘরে বাশ দিই।,0,sports
বাল,0,sports
শুভ কামনা কাটার মাস্টার,0,sports
এত দর্শক মাঠে! ছিঃ ছিঃ,0,sports
শান্ত কে কেন দলে নেই আমি বুঝি না,0,sports
পাপন ভাইআপনি একজন সম্মানিত লোকতাই প্লেয়াররা সরাসরি আপনাকে পদত্যাগ করতে বলে নাই!আপনি এমন বোকার মত কথা বলার ত কিছু নাই!যারা খেলোয়াড়তারা চাচ্ছে না আপনাকেএটাই ত যথেষ্ট। পদত্যাগ করে ফেলেন ভাইয়া।পরে আবার কি কি বের হয়ে যায়😂,0,sports
সাধীনতা তুমি কেন বন্ধি? তুমি কী আইনের নামে দুসকৃতিদের হাতে বন্ধি? সাধীনতা তুমি কী পরাধীনতায় শীকল পরা বন্ধি? সাধীনতা তুমি কী অনন্যায়ের প্রতিবাদী ভাষা কেরে নেয়া একফন্ধি? সাধীনতা তুমি কী অসহায় মানুষের অধিকার আদায়ে মিথ্যা অঙ্খিকারে বন্ধি?,0,sports
দেশের এখন মেরুদণ্ড নেই বললেই চলে,0,sports
আর এক জন ক্রিকেট খেলোয়াড়দের যে মুল্য তা কোন নায়ক নায়িকা জীবনেও পাবে না ওদের পায়ের কাছে যাবারও যোগ্যতা নেই নায়ক নায়িকাদের ঠিক আছে,0,sports
ফালতু,0,sports
রাইট রুবেল ভাই,0,sports
অই বেয়াদব কে জাতীয়টীম <br />থেকে বাধ দেওয়া হোক,0,sports
আমি বুঝিনা করলে সমস্যা টা কি,0,sports
তোর বাবার টাকা বোনাস দিয়েছিস,0,sports
উইকেট পেলো টা আর পিকচার এ দিয়া রাখছেন টা।। গাজা খেয়ে থামলিন বানান নাকি।।,0,sports
আমার মতে বাংলাদেশের কৃকেটাররা যদি সত্যিকারের মানুষ হয়ে থাকে তাহলে সাকিবকে ছাড়া তারা মাঠে নামবেনা।আজ সাকিবের সাথে এইটা হইছে কাল অন্য কারো সাথে হবে। পাপননা সালারপুত সালা তুই যতোদিন বাংলার কৃকেট ভোটে থাকবি ততদিন বাংলাদেশ ফাইনালে জিতার কথা কল্পনা ও করতে পারবে না।আমার তো মনে ঘুসের বিষয় পাপননা নিজিই জরিতো,0,sports
আসল কথা কেউ বলেনা কারণ কারো সাহস নাইমুসলিম দেশে সরকার বা রাষ্ট্র প্রধান মহিলা হারাম আছেএই কথাটা কেউ বলেনা বাংলাদেশে তাহলে দরে নিব পুরুষ লোক নাই। আল্লাহ বলছে যাহারা নারীদের পিছনে থাকবে তাঁহারা কাল কিয়ামতের দিন অবশ্যই জাহান্নামে যাবে। আওয়ামী লীগ এবং বি এন পি দুজনই মহিলা সরকার তাহাদের কে বয়কট করুন এবং পুরুষ শাসিত দেশ গরুন। আল্লাহ সকলকে বুঝার তৌফিক দান করুক।,0,sports
গর্জে উঠো বাংলার মানুষ।বাংলার মানুষ যদি একতাবদ্ধ হয় তাহলে এক পাপনকে বাংলার মাটি থেকে উড়াই দিতে এক সেকেন্ডও লাগবে না।অন্যায় করলেও শাস্তি না করলেও শাস্তি।তাহলে এই পাপনকে দেশ থেকে বিতারিত করে বাংলার মানুষ হাজার শাস্তি বহন করতে রাজি।মিডিয়ার মধ্যে এসে লাফালাফি না করে সে সালের যুদ্ধের ময়দানে একতা হও বাঙ্গালি।জয় আমাদেরেই হবে ইনশাল্লাহ,0,sports
এই বুচকির সাথে ছিঃ ছিঃ ছিশ,0,sports
আওয়ামী লীগকে ক্ষমতায় থেকে নামিয়ে দও,0,sports
সাব্বির ভাই এর কোনো দোষ নায়।সব দোষ বয়সের।,0,sports
সাকিব যখন ছিলনা বাংলাদেশ তখনো খেলছে সাকিব না থাকলে দলের কিছুই হবেনা,0,sports
যেই না চেহারা নাম রাখছে পেয়ারা।,0,sports
আমারা কোন বুজলাম না পাপন কোন মাদার চুদ সে কে তার বাড়ি কই সে বাংলাদেশ টারে ধংশ করতে চাইতাছে আমরা বুজে গেছি রে পাপন চুদির পুত,0,sports
অসাধারণ ম্যাচ হয়েছে👌👌,0,sports
বাংলাদেশের ভালো খেলোয়ার কে রেন্ডিয়ান রেন্ডিরা এসব ফালতু অভিযোগ করে জয় ভেংলা করেই ছাড়বে তা আমাদের খেলোয়াড় গন বুঝা উচিৎ।,0,sports
সাকিব ভাই আপনি প্লিজ কাঁদবেন না। আপনি বীরের মতো দেশের সব ধরণের ক্রিকেট থেকে অবসর নিন। তারপর একজন সাকিবের অভাব হারে হারে টের পারে বাংলার ক্রিকেট।,0,sports
আনামুল বিজয় কে বছর পর দেখলাম। আগের মতই আছে । রান করতে টা ক্যাচ দিসে। একজনকে রান আউট করাইছে নিজের হাতে ডেকে এনে। যন্ত্রনাময় এক ইনিংস।,0,sports
মিডিয়া কুত্তার বাচ্চারা যা করল মানুষ অসুস্থ হলে বলে মারা গেছে আর পাদ দিলে বলে বাথরুম করেছে কি বলব এদের কথা বিশ্বাস করবে কিভাবে মানুষ,0,sports
অমানুষ পাপন,0,sports
তাহলে তারা কি মিথ্যা কথা বলতেছেতুমি পদত্যাগ করোকোন কিছু হলে তুমি বল তুমি জানো নাজানো না কেনো,0,sports
মনে হয় এখনি হার্ট অ্যাটাক করলাম 💔💔💔💔,0,sports
এখানে কারাপের তো কিছু দেকিনা আমি।,0,sports
কুমিল্লার জিততে শেষ বলে রান লাগে সেই সময় বলে ররান করে ওয়াইস তবে শেষ ওভারে রান লাগে কিভাবে সম্ভব জিতা তবে জিতলাম অবশেষে।,0,sports
আমি মুশফিকের ফ্যান ছিলাম। কিন্তু আজ থেকে আর না। খারাপ খেললে সমালোচনা করতেই পারে তাই বলে গায়ে হাত দিতে হবে। এই ফ্যানদের জন্যই আজ তারা বিখ্যাত। মুশফিক কঅত বছর খেলে তা দিয়ে কি করবে। জন্ম থেকেই বাংলাদেশের মানুষ এই দেশের খেলা দেখে। মুশফিককে সংযত হওয়ার দরকার ছিল।,0,sports
রাসেলের ব্যাটিং এর ফ্রেন্ড এখানে কতজন আছেন আমার মত,0,sports
ভাই রে যাদের রোস্ট করেছেন তারা প্রত্যেকজনই ভালো আপনি কতটুকু যানেন? না বুঝে ভিডিও বানাতে আসেন কারণ হচ্ছে আপনি তে জড়াতে চান তাই বলে কি সঠিক যাচাই না করে? এখানে তারেক মনোয়ার তারপর আজহানী তাদের নিয়ে কতটুকু আপনি যানেন? আপনি কি ইসলামের দাওয়াত দেন? নিজেই তো ইসলামের দাওয়াত দেন না আবার ইসলাম ভক্তা নিয়ে সমালোচনা করতে আসছেন। ইসলাম নিয়ে কতটুকু যানেন আপনি আপনারা ইসলামের দাওয়াত দিবেন কিন্তু অন্য জনকে করতেই দিবেন না। বলতেসেন তাদের কি যুগ্মতা আছে? তারেক মনোয়ার আজহারী তাদের যেই যুগ্গতা আছে তা আপনার নাই,0,sports
সানটো জটিল,0,sports
পাপন ভাই খেলা ডাইরেক বন্ধ করে দেন এত টাকা খরছ করে এই বালের খেলা আমরা চাইনা,0,sports
আই লাভ চিটাগাং টিম,0,sports
মিস্টার ফিনিশার,0,sports
বিপিএল এর প্রথম সুপার ওভার ❤❤,0,sports
পুরাই প;য়ের পাগলামি।পাপনের পায়ে পারাপাবিনা পাড় পোলাপানপাঠক্ষেতে পায়জামা পরা পাছা পাঞ্জা পৎ পৎ।পেটেপিঠে পীঠটান।শাকিব আল হাসা😪😪😪🤑🤑😤😤😤,0,sports
ইমল ব্রো না থাকার কারনে জিতে গেলি।,0,sports
ইনশাআল্লাহ এইবারের ট্রপি যেন চট্টগ্রাম পায়,0,sports
আমার তো মনে হয় পাপন নিই সাকিব ভাইকে ফাশানোর জন্য ই ওই জুয়ারিকে বলছে এই কাজ টা করতে যে ওই জুয়ারি যেন সাকিব ভাই কে এই অফার দেয়,0,sports
পাপন তোমাকে চাইনা গিলটি,0,sports
কত জন কে কোটি দিছেন? একক প্রতিষ্ঠান আপনার এটা?সমস্যা কোথায় বুঝেননি ? আপনার দুনীতি ধরা পড়ছে ? আপনার পক্ষে একটা লোক নাই কেন? হাস্যকর,0,sports
পাপনের পদত্যাগ করা উচিত। সাকিবের মত ভালো খেলায়র হয় না।,0,sports
ভাই আপনার কাছে একটা রিকুয়েস্ট শুধু পাপুন্দারে নিয়া একটা রোস্টিং ভিডিও চাই।।ক্যাসিনো কান্ড নিয়া।ভিডিও চাই পাপন এর।।।।পাপন্দার পদত্যাগ চাই।,0,sports
পাপনের পদ্ত্যাগ চাই,0,sports
বালের হাইলাইট খেত হালারা বাউন্ডারির ভিডিও বানাচ আবর টচ দেখাচকেন ভুলে ভরপুর বালের ভিডিও বানাচ,0,sports
সাকিব তুমিই সেরাতুমি আসবে রাজার মতোই,0,sports
পাপনকে কাড গরায় দারানো উচিত।।।। সব দস সাকিবের হলে বি চি বি এক নাবারে আসবে,0,sports
দরি মাছ নাহি ছুই জল। পাপন দেখাইলা,0,sports
আশরাফুল ভাইর মত সাকিব ভাইকে ও হারাতে চাই না ক্রিকেটে রাজনিতি বন্ধ করেন পাপন কাক্কু আম্মের মিডা কতা আর জাতি শুনতে চায় না,0,sports
রাসেল এর ইনশাআল্লাহ বলাটা শুনে অনেক খুশি লাগলো,0,sports
হায়রে মানুষ রঙ্গীন ফানুস,0,sports
ভাবতেই অবাক লাগে।বাংলার দুই তারকা আজ দেখাই দিল লম্বা দিয়ে সব হয় না মনের জোর আর পরিশ্রমেই সব।,0,sports
মিরাকেল মিরাকেল,0,sports
মেয়েটার চরিত্র দেখে বুঝা যাচ্ছে এটাই তার প্রাপ্য ছিল এদেরকে খারাপ বলার মতো কোন ভাষা নেই,0,sports
বস আবার ফিরে আসো।দোয়া করি,0,sports
শেষ পর্যন্ত রাজশাহীর রয়েলস কাপটা নিয়ে গেল খুলনার কাছ থেকে খুবই খারাপ লাগছে আমার কাছে।,0,sports
এই এ সবচেয়ে ভালো লাগছে যে নিজেদের খেলোয়াড়দের সুযোগ দেওয়া হচ্ছে 😍😍😍,0,sports
চুতিয়া বেচমেন,0,sports
অনেকেই অনেক ধরনের কমেন্ট করেছেন নাসিরের পক্ষে।আসলে যথার্থ না জেনেই না বুঝেই দোষ গুলি মেয়ের চেপে দিছেন।আসলে এই কথোপকথন এর উদ্দেশ্য টা বুঝছেন?কল কিন্তু নাসির দিছে।এই কথোপকথন আপলোড দিছে নাসির।নাসির প্লান করেই এটা করেছে।কারণ নাসির এখানে নমনীয় সে বার বার বলছে একটা শান্ত হও আমার কথা শুনো মেয়েটা শান্ত হইলেও নাসির কিছু বলে না।কারণ কি?প্রেম ভাই করেছি ব্রেক আপও হইছে।একটু হলেও জানি প্রেমের জ্বালা কি?মেয়েটা বুঝতে প্রেমের জ্বালা টা কি?নাসির আগে যে বকা খারাপ কথা বলেছে সেগুলো এই কথার মধ্যেই বোঝা যাচ্ছে।নাসির পাবলিকের কাছে ভালো সাজার জন্য এই কথোপকথন টা আপলোড দিছে।মেয়েটা গালী দিছে ঠিক আছে।কিন্তু কেন দিচ্ছে সেটা অনুধাবনের বিষয়।।।রিয়েল লাভ করলেই কেবল কান্না করা যায়।নাটক করে অঝরে পানি ফেলা যায় না বুঝতে হবে।।যাই হোক আমি চায় তাদের ভিতর সম্পর্কটা ভালো থাক।আমি এখানে মেয়েটার পক্ষ নিয়ে কিছু বলতে চায় নাই।আমি জাস্ট এই কথোপকথনের পরিপ্রেক্ষিতে বলছি।নাসির ভাইকে আমারও ভালো লাগে।খেলা দেখি।কিন্তু এমন টা করা ঠিক হয় নাই।ভালো সাজার জন্য আপনি এখন সাধুসন্ন্যাসীর মতো ভাব ধরে কথা বলেছেন।।খারাপ কিছু বলা হয়ে গেলে সরি।,0,sports
কতো মানুষ বকে সেটা কিছু না বাল সাল অজথা ওনাকে হয়রানি করে,0,sports
পাপন কি হাসিনার জামাই????,0,sports
আমার মনে হয়ে কোহলিরও অনেক কাণ্ডকীর্তি আছে কিন্তু ওনার মেধা আছে বলে উনি বেচে যান।আজ সাব্বিরের মেধা বেশি থাকলে হয়ত সাব্বিরও বেচে যেত আর এই খবরে Youtubeএর ওপর ১মিলিয়ন ভিউ হতো না।যাই হোক আন্দাজে বললাম।,0,sports
যার নাম পাপ দিয়ে শুরু সে পাপই করবে।পাপন এর মুখে জুতা মারলেও কম হবে,0,sports
ছিলামআছি এবং থাকবো!!!তুমি সত্যতুমি সাহসী তোমায় অনেক বেশি ভালবাসি সাকিব,0,sports
ভালোবাসার আরেক নাম রাজশাহী,0,sports
কথাটি সেই ছিল 😃,0,sports
সাব্বির এর মত ক্রিকেটে বাংলাদেশ কোন প্রয়োজন নেই,0,sports
মেহেদী দারুন খেলছে আশা রাখি তাকে দেখব জাতীয় দলে,0,sports
বিসিবি অন্ধ পাপন কে বহিষ্কার করে মাশরাফি কে দেওয়া হোক দায়িত্ব,0,sports
পাপনের যায়গা পুরন করা বাংলাদেশে অনেকেই আছে সুতারাং সকিবের যায়গা পুরন করা এমন কেউ আছে কি পাপন?পাপন তোরও এরকম সময় একদিন আসবেই অপেক্ষা পোরহর গুনতে থাক পাপন আজ তোর জন্যেই অবস্থা,0,sports
কইএকটা সালা আচে বাংলাদেশে সেই সালারা বাংলাদেশকে খারাপ করচে,0,sports
"হ্যাপী এখন মুফতি,রুবেল এখন বিবাহিত",0,sports
আসলেই ক্রিকেটের ইমেজ নষ্ট হয়েছে।দাবি গুলো আগে বিসিবি কে জানানো উচিত ছিলো না মানলে তখন আন্দোলনে যেতে পারতো।,0,sports
রাজশাহী জন্য শুভ কামনা রইলো,0,sports
রুবেলের ভাষা শুনে অবাজ হচ্ছি।ঘৃণা হচ্ছে।এরা নাকি জাতীয় খেলোয়ার!,0,sports
নাজমুল হাসান পাপনকে গতি থেকে নামানো হোক,0,sports
আরে বেটা দেশে মাডার করলে বিচার হয় না গালীর বিচার নিয়ে টানা টানি করচ,0,sports
তুমিমামুমিঠামিঠাকথাবল্লেকাজহবেনাতোমারপদোতেগচাই,0,sports
টি দাবির মধ্যে সাকিব টি সত্য কথা বলাতে বি সি বি গায়ে বাধে! কথাটি হল ম্যাচ শুরু আগে ফলাফল হয়ে যায়! আমার মনে হয় সাকিব নয় আই সি সি বি সি বি প্রধান কে আজিবন নিষিদ্ধ করা দরকার? যদি জানতাম আই সি সির নাম্বার তাহলে কোটি বোটারের মতামত দিতাম।,0,sports
"সিজদা যে দিলো,সেটা দেখেন না??",0,sports
সাকিব ছাড়া বাংলাদেশ ক্রীকেট অচল,0,sports
যারা কমেন্ট করলো ওরা নাকি ফ্যান 😂😂,0,sports
আন্দ্রে রাসেল কি ইঞ্জুরিতে নাকি,0,sports
যত সব ইজিবিজী কথা,0,sports
এটাকি বোর্ড সভাপতি নাকি বিশ্লেষক???এলোকের এত কথা বলার কি দরকার?? তার তো দরকার ছিল বোর্ডেরর সাথে সম্পকিত সে সকল দায়িত্ববান লোকদের কে এসব কেন হল সেটা জিঙ্গাস করা।।ছাগল দিয়ে কি হাল চাষ হয়?? পাপন সাহেব কি আসলেই ক্রিকেটিয় ঙ্গান সমৃদ্ধ?????,0,sports
পাপনের মুখে জুতা মারো তালে তালে,0,sports
না দরকার ছিল। কারন কোন ব্যাটসম্যান যেখানে দাড়াতেই পারেনি সেখানে সাব্বির এত ভাল একটা ইনিঙ্স খেলল আমার মতে টিক আছে,0,sports
যে ভাবে নাচতেছে যেন খুব ভার প্লেয়ার,0,sports
আমরা বাংলা জতীরা পারিও বটে। আরে আগে মানুষকে সম্মান করা শিখে খেলা দেখতে যাইছ স্টেডিয়ামে। বেটা ছাগল। তুই কি বাল ফালাইছস তুই ক্রিকেট শিখলি না কেন। তুই আইসা বাংলাদেশ দলে নে। সেটাতো পারবি না।পারবি বাল পাকনামি করতে। ছাগল,0,sports
ইন্ডিয়া সফর বাতিল হলে বাংলাদেশ এিকেট টিম একদম শেষ হয়ে যাবে,0,sports
অনেক সুন্দর খেলা হইছে,0,sports
নাজমুল হাসান শান্ত গরিবের রিসাব প্যান্ট,0,sports
এইসব কাজ করার সময় আবেগ কোথায় ছিল,0,sports
এটা ভারতীয় মিডিয়া ও পাকি দের চাল,0,sports
মোহাম্মদ নাইম ভক্ত গুলা কই লাইক দিন,0,sports
ভাই আমি যদি আমার থামনেলে আপনার ছবি দেই আপনি কিছু মোনে করবেন,0,sports
আবার সাবস্ক্রাইব করলাম;,0,sports
ভাই তাসকিন কি জে মজা আমি পাইলাম রে 😂,0,sports
সময়টা এখন পাবলিক সাংবাদিকেদের?,0,sports
আলহামদুলিল্লাহ খুশি হলাম কুমিল্লা জিতাতে। অনেক ভালো লাগলো।। শুভ কামনা রইল কুমিল্লা ওয়ারিয়র্স দের জন্য।,0,sports
দালালদের ভাব যে কি,0,sports
সৌম্য দা😘😘😘😘😘,0,sports
মাশরাফিকে বোর্ড সভাপতি বানানো হউক।,0,sports
এইটা বাংলাদেশের মানুষ জানে এইটা কার কাজ এই সময় যোদি সাকিবের পাসে বাংলাদেশের মানুষ না থাকে তাহলে আমরা আরেক জন আসাফুলকে হারাব আর পাপন সাহেব ত বলেই দিলেন তারাতারি খবর আসবে এইটা কি দফায় মদ্দে পরে,0,sports
পাহাড়সম রান করে ঢাকাকে হারালো চট্টগ্রাম পরাজয়ের হাট্রিক রংপুরের।,0,sports
বাংলাদেশ আর জিত্তে পার বে না,0,sports
বলছেন ছোট্টো মিরাজতার সাহস কত যে বিবিসি প্রধান এর ফোন রিসিভ করে নামিরাজ এর টিম এ থাকার কোনো অধিকার নেই; ;,0,sports
চিটাইংগা ফুয়া মেডিত ফৌইললে লুয়া💪👌✔️,0,sports
মুশফিকের জার্সি পরা হালায় দি বড় দালাল,0,sports
ওপেনার বেসমেন্ট এ রখমি দরকার উরাদোরা মাইর।,0,sports
বিসিবির এত এত টাকা আছে।এসব টাকা কোথায় খরচ করে এইটা জানালে ভালো হতো। এতই যদি কাজ করে তাহলে বিভাগীয় পর্যায়ে ক্রিকেটের এই অবস্থা কেন?,0,sports
মুশফিক বাংলাদেশের সেরা ব্যাটসম্যান❤❤,0,sports
অসাধারণ লাগালো আমির ভাই আপনার বোলিং। এই রকমের বোলিং কুখ্যাত ভারতের বিরুদ্ধে দেখতে চাই!!!,0,sports
আমি গালি দিতে পারি যদি তার খেলা খারাপ হয়,0,sports
পাপনের এই কাজটি বালো করেনি সাকিবল হাসান একজন সত লোক,0,sports
আজ থেকে আর কখনো বাংলাদেশের ক্রিকেট খেলা দেখবোনা।,0,sports
নবীকে গালি দেয় কারও গায়ে লাগেনা ক্রিকেট খেলা হারাম সেই খেলোয়াড় কে গালি দিয়েছে দেখে কি অবস্থা আমরা অনেকেই জানিনা যে ক্রিকেট ফুটবল খেলা হারাম যেই খেলাতে টাকা লেনদেন হয় সেই খেলা হারাম আর আমরা হারামির জন্য লড়াই করি।,0,sports
সালারা গান কই,0,sports
ইংল্যান্ড এ খেলতে হইলে সাকিবকে আবার জন্ম নিতে হবে।ওদের সামনে সাকিব বাচ্চা,0,sports
শাউয়ার পোলা পুরান জিনিসে হাত দিয়া আবার গন্ধ বার কর কেন...<br />বাইঞ্চোদ নতুন কিছু কর,0,sports
কেন ঘুস নিব কেন ঘুস দিব অন্যর কাছে মাথা নত করব কেন??সাকিব আল হাসান সত্য ন্যায় নিষ্ঠা যে সাকিব আল হাসানকে নিষিদ্ধ করেছে তাকেই নিষিদ্ধ করপাপন কে বহিষ্কার করে পাপন চির তরে বিদায় দিন নইলে পাপন যে জুয়া খেলা শুরু করেছে এমন একটি দিন আসবে টাকার জন্য বাংলাদেশ দল কে বিক্রি করে জুয়ার আসরে খেলবে,0,sports
রাজশাহীর মামুরা লাইক আর চাঁটগাইয়া বাবুরা কমেন্ট করুন । ঝড় উঠবে ।,0,sports
আজকে থেকে বাংলাদেশের খেলা আর দেখবো না।পাপন সাহেব আপনাকে ধিক্কার জানাই।দুই বছর আগের ঘটনা নিয়ে এখন কেনো পাপন সাহেবের এতো মাথা ব্যাথা আসছে।,0,sports
সাবির কুতার বাচছা কমেট গুলা দেখিছ তর বাপেরা কি লেকছে,0,sports
জাহা বলছে ঠিক বলছে বাল খলছে আমি হলে আর খারাপ কিছু বলতাম এর নিশা খোর হালর পুত কি করে দেখছেন,0,sports
এই এ ম্যাচে রান করছে 🏏,0,sports
সাব্বির আমার সোনার হিটার,0,sports
তাসকিন একটা গাধা তাহলে এসব ভিডিও ছাড়ে,0,sports
এটাই বাংগালি জাতির ধরমো নিজেরা কিচু করতে পারেনা আরেক জনকে নিয়ে সমলোচনা করতে পারে ঠিকি,0,sports
জবাবটা যেকারনেই দিক ভাল লাগছে,0,sports
স‍্যার এদের সব টি বাদ দিয়ে নুতুন দের সুযোগ করে দিন এবং তাদের কে নিন যারা আগে দেশকে ভালবাসবে টিকেট খেলা টাকে ভালবাসবে তার পর টাকা বিষয় আসবে ।,0,sports
অভিনন্দন রাজশাহী কে অভিনন্দন আন্ডে রাসেল,0,sports
আমাদের দেশের মুসিকে সিরিজ দেয়ার দরকার ছিল কষ্ট পাইলাম,0,sports
সাকিব কে বাদ দিলে আগুন জ্বালিয়ে দিব।,0,sports
ঢাকার কেকে আছো লাইক দাও 👍👍👍,0,sports
আমি দিলাম বর্তমানে এর চেয়ে ভালো এ করা বলার খুজে দেখান।কেও পারবেন না!!!,0,sports
ইন্ডিয়াতে ধনির বাড়ীতে কত বার হামলা হইচে আরো বেসি কিছু হয় বাড়ী ঘরও বাংচুর হয় কিন্তু সে হিসেবে চেলেটাকে হয়রানি করার দরকার চিলোনা সে ইচ্ছে করলে মান হানির মামলা করতে পারবে মশফিক পারবেনা,0,sports
সাকিব কি তুর বোনের জামাই লাগে আই চিটাগাং পোয়া,0,sports
ভাই এগিয়ে যাও,0,sports
আগামীর ভবিষ্যৎ হবে নাইম,0,sports
পাপন সহ ক্রিকেট বোর্ডে সবাইকে পদত্যাগে দাবী জানাই।,0,sports
"সাব্বির যদি এই উদ্জাপনটা নাকরতেন তাহলে তার সম্মান আরো বেড়ে যেতো,,কারণ ম্যাচটা হেড়ে যাচ্ছিলো।",0,sports
পাপন হটাওক্রিকেট বাচাও,0,sports
লোকমান কেসিনো ভাড়া দিছে আর আমি খেলেছি হা হা হা।,0,sports
বিসিবির চোখ কানা কুমিল্লা বুওলার নাই এক যন মযিদ বাচ,0,sports
পাপনের পদত্যাগ চাই ইমরুল কে দলে চাই,0,sports
ভাংলা বাঘ দাইফিজ,0,sports
পাপন আর ভারতের চক্রানের বলি হলেন সাকিব।,0,sports
পাপনের কিছু কথার সাথে আমি সহমত পোষণ করছি পাপন সাহেবের পদত্যাগ চাই,0,sports
আপনি সঠিক কথা বলেছেন ভাই,0,sports
পাপনের পদত্যাগ চাই ভাই আমরা।হ্যা ভাই সাকিব না থাকলে বাংলাদেশের ক্রিকেটের অনেক বড় ক্ষতি হয়ে যাবে।,0,sports
সাকিবের ব্যাপারে পাপনের হাত নেই। তবে সে চাইলে শাস্তি কমাতে পারতো এটা ঠিক।,0,sports
পাপন জুতামেরে গুরুদান,0,sports
সাকিব সাহেব না সাকিল সাহেব,0,sports
পাপনদা তুমি সুধু সাকিব না বাংলাদেশ ক্রিকেট টিম কে ধংশ করছো।তুমি তো দেখি রাজাকারের হাল ধরছো,0,sports
এটা কি হল এখন যদি সবাই মুশফিকের চৌদ্দগুস্টি উদ্ধার করে কি করবেন আপনারা,0,sports
একমত না,0,sports
শাকিব আল হাসান ইংল্যান্ড এর দলে খেলক আমরা চাই।,0,sports
গ্যালারি তে মানুষ ই নাই বালের বিপিএল😆😆,0,sports
কমেন্ট করতে দিসে নিজের মতামত জানার জন্য আর এখানে আবাল গুলা আসে লাইক ভিক্ষার জন্য।,0,sports
এর যত্ন নেওয়ার দরকার র তাহলে ভালো কিছু দিতে পারবে বাংলাদেশ দলকে,0,sports
দেশের প্রধানমত্রী তো এই পাপইন্নাহালায়ি সব সমস্যার সমাধান করে।,0,sports
অনেক ক্ষতি হবে বা হচ্ছে।।,0,sports
পুরান দল বাদদিয়ে নতুন দল গঠন করেন,0,sports
খুবই কঠিন ভিডিও লিংক,0,sports
স্পট ফিক্সিং ম্যাচ আন্দ্রে ফ্লেচার মিথুন রাদারফোর্ড এর ব্যাটিং একটু ভালোভাবে দেখলেই বুঝা যায় এর পর আবার সুপার ওভারে কি চোদাইন্না খেলাটা খেললো এক মাইরা আর কোনো রান নেওয়ার ইচ্ছেই নাই সুপার ওভারে রে না নামায়া রাদারফোর্ড বাহ হোয়াট আ ম্যচ দিজ ইজ🖕,0,sports
বালের সাকিব রাকিব ক নিয়ে এত চিন্তা করে কি দেশের কি অবস্থা সেই গুলা একটু চিন্তা করেন সবাই টাকার জন্য মাঠে নামে ভাই অন্য কিছুই অন সম্মান কেউ চিন্তা করে না বালের কাকী অমর,0,sports
সিলেট হার,0,sports
বিদেশি কোচ আনার পরেও যদি আপনি মাতব্বরি করেন তাহলে ত এমনই হবে? পাপনের পদত্যাগ চাই। বছর ধরে দায়িত্বে থেকেও বলেন সমস্যা সাময়িক?,0,sports
অরে ভাই রে সাকিব বাংলাদেশে না খেললে আর কে খেলবে রে ভাই?সাকিব ভাইকে বুকে নে রে ভাই।সাকিব ভাই আমাদের কাছ থকে চলে গেলে কখনো জয়ের মুখ দেকতে পারবো না রে ভাই। সাকিব ভাই যেন কোথাও না যেতে পারে সাকিব ভাইকে আটকা রে ভাই।অরে ভাই রে কেনো বুঝজ না রে ভাই সাকিব ভাই বাংলাদেশে না থাকলে কে বাংলাদেশ টিম নষ্ট হয়ে যাবে রে ভাই।,0,sports
পাপন সালার ভুতকে আমি কি করো আমি জানি না,0,sports
এতদিনে বাংলাদেশের ক্রিকেট টারা একটা ভালো ডিসিশন নিচেবাল পাকনা সভাপতি পাপন সহ সবাইর পদত্যাগ দাবী করছি।,0,sports
একটা ভাল খবর সাববির ফমে ফিরেছেন।,0,sports
সাকিব বাই আমরা আচি তোমার সাতে আবার পিরে আসো আমরা তোমাকে অনেক লাপ করি,0,sports
এরে রুবেল,0,sports
রাসেলের জন্য কাপ নিতে পারলো রাজশাহী,0,sports
পাপনের পিছে লাগছে আগুন 🔥🔥🔥এইবার দেখি আপনার ভিডিও টায় পাপনের বিপক্ষে কি পদক্ষেপ নেওয়া হয়। আর সাকিব ভাইয়া আবার ফিরে আসে কিনানাকি ভিডিও পাও করা হচ্ছে।,0,sports
একটা ছেলে বলতেছে গালি দেয় নাই।কছম করে বলতেছে তাও তাকে জোর করে স্বীকার করাইতে চায় সে গালি দিছে। আর বালের সাংবাদিক ইউটিউবারও ক্যাপশন দিছে!!!! এদের খাইয়া কোন কাজ নাই ইউটিউব চ্যানেল খুলে উল্টা পাল্টা নিউজ আপ্লোড দেয় টাকা কামানোর জন্য। দালালি ছাড়া এদের ভাত হজম হয় না।,0,sports
কেন তার কা অদিকার নেই প্রথম ১০০ মেচ হারছে সে কি খারাপ খেলছে,0,sports
সাকিব কে বাদ দেওয়াই উচিত,0,sports
সাক‌িব তুই চ‌িন্তা কর‌িস না। শয়তার সব সময় ভাল‌ো মানুষ‌ের পিছন‌ে লাইগা থাক‌ে । আর তুই হল স‌েই মানুষ। ক‌োটি মানুষ তর সাথ‌ে,0,sports
"বাংলাদেশের মিডিয়া হল মাদারচোদ। দেশের আর কোন বাল পায় না রিপোর্ট করত। <br />ভাই যারা প্লেয়ার তারা তো মানুষ।<br />পারস খালি এই বাল ই। <br />সময় টিভি আজ পর্যন্ত কোন ভালো এবং নির্ভেজাল কোন সুংবাদ দিতে পারে না।<br />দেশ এ যে দুর্নিতি হইতাসে তাতে তারা কোন বাল ছিরে না। খালি দেখব সাব্বির,নাসির,মোসাদ্দেক কি করল।<br />আবার সাব্বির দলে ফিরুক পরে ঠিক ই কুত্তার মত আবার জয়গান গাইবো।<br />বালের দেশের বালের মিডিয়া",0,sports
আপ্নার কথা শুনে অনেক কস্ট লাগলো ভাই।আবেগিত হয়ে গেলাম,0,sports
ভাই এটাও ইন্ডিয়ার সকরানতো,0,sports
রিপোর্টারের গার্লফ্রেন্ড ভাগছে মনে হয়।ফ্যানরা ছবি তুলতেই পারে ভাই,0,sports
জাতীয় দলে আইলেই তো ছাগল হয়ে যায় সব,0,sports
"ফকিরনীর পোলার ফর্ম নাই। তাতেই এই অবস্থা। আর যদি তামিম, সাকিব, মুশফিকের মত ফর্ম থাকতো - তাহলে আর ওকে থামাইতো কে?",0,sports
ভাই আপনি ঠিক বলেছেন। কারণ ইশারাকে অনেক ভাষা দেয়া যায়।।,0,sports
পাপন সাহেব টিম এর কিছু আবাল প্লেয়ার বাদ দেন। রিয়াদ কি করে চাঞ্জ পায় ? প্রশ্ন আপনার কাছে ওকে আগে বাদ দেন আর পেস বলার নাই কেন,0,sports
ভারতে সাতে হাত মিলে এই কাজ করতেছে পাপন,0,sports
এমন ক্ৰিকেটাৰক শাৰীৰিক শাস্তি দিয়া উচিত ।,0,sports
শালা পাপন তুই তর বেক্তিগত যামেলার কারনে সাকিবকে ফাসাইসস সাকিব এর পরিবের্ত তুই গিয়া খেলিস। দেখি মেচ জিতাইতে পারস কিনা।তুই এত দিন ঘুমাইসস নাকি এত দিন খবর ছিলনা তর সাকিব আন্দোলন করার পর তর খবর হইছে,0,sports
সবাই বলছে সাব্বিরের কারনে কুমিল্লা হারছে আসলে সেঠা না সাব্বির যখন আসে তখন সাব্বির যেমন খেলছিল তখন সোম্য একিরকম খেলছিল এই বিপিএল এ সাব্বির এর একেবারে যখন সে ব্যটিং এ আসে তখন সে ক্রিজ এ নতুন এসেছিলো তখন এই সময় সোম্য এর দায়িত্ব নেওয়া উচিৎ ছিলো যখন সাব্বির অাউট হলো তখন সোম্য হাত খুললো সাব্বির যখন ছিলো তখন যদি সে হাত খুলতো তখন সাব্বির তার ফিরে পেত।,0,sports
সেরা বোল উইকেট ছিলো শোয়েব মালিককে ক্লিন বোল্ড!! ❤❤👌👌✌✌✌,0,sports
আমি চাই বিসিবি দুর্নিতি যুত্ত থাকুক,0,sports
পাপন কাক্কুআপনি ঠিক আছেন ত্য 😂😁😂,0,sports
তাসকিন একটা ফালতু,0,sports
ভারতে প্লেয়ার খারাপ খেল্লে গাল দিলে কেও কিছু বলে না আর বাংলা দেশের গার পাকামো যত সব বালের মুশফিক কে গাল দিঃয়েছে ঠিক করেছে,0,sports
ছিছিছি লজ্জা করলো না।,0,sports
তোমাদের প্রেম লাইলি মজলুর মতো হতে যাচ্ছ,0,sports
বিপিএল এ দর্শক নাই আজহারি হুজুরের মাহফিলে দর্শকদের বসতে দেওয়ার জায়গা নাই লাখ মানুষ হয়েছে মাহফিলে।,0,sports
এক দফা এক দাবি পাপনের পদত্যাগ চাই,0,sports
রুবেল।আর।নাসির<br />।দুনুটায়।একরকুম।,0,sports
যদি ধারাবাহিকতা রাখতে পারে তাহলে তার কাছ থেকে ভালো কিছু আশা করা যায়,0,sports
বাবার বিরুদ্যে কথা বললে এটা হবে।,0,sports
তাসকিনকে কেনো খেলানো হচ্ছে না?,0,sports
কাজ টা ঠিক হয়নায়,0,sports
হাই ওয়ান রোবেল,0,sports
পাপন ক্যাসিনো খেলোয়াড়,0,sports
গাজা খাইছো না কি,0,sports
পাপন কে বিসিবি থেকে বরখাস্ত করা হুক,0,sports
কাজটি ঠিক হবেনা। ক্ষমতাসিনদের নাড়াচাড়া করতে না গেলে হয়তবা এমনটি নাও হতে পারত। এতদিন পরে কেন????,0,sports
ও আমার চেহারার অবস্থা,0,sports
কে এই আগারওয়াল???,0,sports
এটা ঠিক না ভাই,0,sports
সেম বিসিবি,0,sports
আমি চাই যে সাকিব ইংলান্ডের হয়ে খেলুক।তখন দুরনিতিতে বাদ পরবে না।,0,sports
"ভাল করছে সালা গরীব, বেয়াদব, রোমিও, দেখে মনে হয় মাগীর দালাল, আজীবন এর জন্যে নিষিদ্ধ করা হউক।",0,sports
কুমিল্লা সেরা হবে,0,sports
মুসফিক কে গালি দেয় নাই বলছে মুসফিক কিছু বলতেছ না বাইরের শালারপুতারা এত বারাবারি কেন আর গালি দিলে হইছেটা কি পিলিয়েররা যখন খারাপ খেলে তখন বলেনা তাদেরকে জা টাকা পলট দিচছে তা ফিরীয়ে নাও তখন কাকে ধর,0,sports
ঝামেলা না করে আপনারা সমস্যা সমাধান করেন আমরা সুস্থ ক্রিকেট চাই,0,sports
সবসময় আমি আন্দ্রে রাসেল কে পছন্দ করি কারণ আন্দ্রে রাসেল যেকোনো সময় খেলা ঘুরিয়ে দিতে পারে সেটা আইপিএল বিপিএল অথবা বিগ ব্যাশ যেখানেই থাকুক না কেন,0,sports
"হুম ভাই আপনার কথা ঠিক আছে ১০০%,আসলে ভাই আমাদের বাঙালীদের একটা জাতি গতো সবাব আছে আর সেতা হলো, সমোলচনা,আসলে কেউ যদি কোনো ভালো কাজ করে বা খারাপ কাজ করে তাহলে শুরু হয়ে যায় তাকে নিয়ে তুমুল সমোলচনা, নানান দরনের কথাবার্তা, আসলে বিশ্বে যদি সমোলচনা নিয়ে কোনো চেমপিয়ানসিপ চালু থাকতো তাহলে বাঙালী জাতি ১নাম্বার স্তান টা দখল করতো ১০০%, বাঙালী জাতি হিসেবে আমরা সেদিন ই উন্নতি করতে পারবো যে দিন আমরা একে অন্যের বিরোধে সমোলচনা করা বন্ধ করতে পারবো,এবং বিশ্বের কাছেও সুনাম অর্জন করতে পারবো।আমার কথায় কেউ মনে কষ্ট নেবেন না।ধন্যবাদ।।।।।",0,sports
এটাতো একাত্তর টিভি বাংলাদেশের সব নিম্নস্তরের টিভি চ্যানেল টিভি সাব্বিরকে নিয়ে এত সমালোচনা কিসে তাদের জলে তাদের হিসেবে খেলতে পারবে লিটন দাস তিন ম্যাচে তিন রান করেছে কিন্তু মিডিয়া কিন্তু এসব কথা বলে না জীবনের প্রথম সেঞ্চুরি একটু খুশি তো হতেই পারে,0,sports
নিয়ে ভিডিও বানান,0,sports
পাপন তুমি যতই নিজের সাফাই গাও আমরা জনগন বুজতে পারি বিসিবির মধ্যে কালো ভুত ঠুকেছে।,0,sports
ভাই ভাইরাল,0,sports
"<b>;;;;;;এতো দিন এই কথা গুলি কই ছিল,,,আজ বলতে আসলো,,,,আসলে সাব্বির অনেক খারাপ,,তাকে ক্রিকেট থেলে নিষিদ্ধ করা উচিত,,,,,,</b>",0,sports
এইটা কি বুঝতেছিনা জনগনের টাকার চাকর আর এত ভাব নিসে,0,sports
সাব্বির  কি বিরাট কহেলি নি তাকে দলে রাখবে। লাথি দিয়ে দল থেকে বের করে দেওয়া হক।,0,sports
পারছে পাপনের দুস,0,sports
ভাইয়া যেদিন মাশরাফি ভাই টি থেকে অবসর নিয়েছিলেন সেদিন খুব কেঁদেছিলাম।আজ সাকিবের জন্য কাঁদলাম।পাপন সাহেব আর কত আমাদের বড় ভাইদের বিরুদ্ধে ষড়যন্ত্র করবেন?,0,sports
বিয়াদব তোকে জুতা পীটা কোরমু তোকে বলসে এইসব কথা🇧🇩 🏴󠁧󠁢󠁥󠁮󠁧󠁿,0,sports
গাদা তর কথা সুনতে মনচায়না,0,sports
মেয়েটা পুরাই ফালতু,0,sports
সোজা কথা বাংলায় কন,0,sports
এমন খেলা তো আমরা প্রাইমারী স্কুলে খেলেছি,0,sports
হু যেত যানে সাব্বিরের ড্রাইভার না যারা দেশের জন্য এত ম্যাচ জেতাই তাদের নিয়ে এইসব ভিডিও বানাতে লজ্জা করে না..... আর কে জানে যে এই ভিডিও বানাইছে সেও কত লোকের বাসাই রাত কাঁটিয়েছে,0,sports
তুরে পাইলে জুতা মারতাম সবাই মারা গেছে।তুই মরছ না,0,sports
এর দেখলেই কেমন জানি পেট ব্যথা করে,0,sports
এটা কোন আবাল মার্কা খেলা।।। বা র খেলা।।,0,sports
গালি দিছে তো কি হয়েছে। শুন্য রানে আউট হলে তো সবাই গালি দেয়,0,sports
মিরাজ জায়গায় বিপ্লব ভাল করবে।,0,sports
বাংলাী হলে লাইক দিন,0,sports
আমি মনে করি বাংলাদেশ ফুটবল টিমের খেলোয়াড়েরাও এইভাবে আন্দোলন করা উচিতকি বলেন সবাই??,0,sports
সাব্বির আর রুবেল দলের জন্য বোঝা হয়ে দাড়িয়েছে,0,sports
সাবিকে বাদ দিলে খেলা দেখবো না,0,sports
পাতনো খেলা এগুলো,0,sports
তাহমিদ আমিদ ভাই পাপন কাকা কে নিয়ে ক্যাসিনো একটা বানান দয়া করে।,0,sports
আপু তোমি কি বিয়ে করবা<br />তাহলে ডিবাই আস কেমন<br />ভাল ভাল সুনা পাবে<br />আরও অনেক বড় সুনা,0,sports
আপনার মতামত ডিক আছে,0,sports
এরকম মজা আমার একদম পছন্দ না তাই খুশি হতে পারলাম না তাই তোমাদের জন্য গুড় আর রইলো না।,0,sports
মাঠ কাপিয়ে দিল ঢাকা 🎉,0,sports
কি দরকার গালি দেওর,0,sports
দুই দিকেই ভালো সুইং করাতে পারে। অনেকটা বোল্ট এর মতো বল করে।,0,sports
সাকিব ভাই বাংলাদেশ দলে যদি না খেলে বাংলাদেশের খেলা আর দেখবো না,0,sports
পাপনের পদত্যাগ চাইএটা সম্পূর্ণভাবে নিশ্চিত যে এটা পাপন কাক্কর কাজ,0,sports
কথাগুলা সত্য,0,sports
মাথা খারাপ হয়ে গেছে ওদের😠😠😠😈😈😈,0,sports
"বিসিবি,র উচিৎ উক্ত ব্যাপার গুলি শক্তহাতে হস্তক্ষেপ করা। দিন দিন বাংলাদেশের ক্রিকেট কলঙ্কিত হচ্ছে ক্রিকেটার দের দ্বারা। এসব actually মেনে নেয়া যাচ্ছে না।",0,sports
দেখে নাকি আবার মেয়েরা পাগল হয় ?,0,sports
লিংটাতে ক্লিক করুন খুব কস্টের,0,sports
আপনি কিছু জানেন না তাহলে কি বাল তুলতে আছেন এখানে,0,sports
পাপন কে জুতা মারা দরকার,0,sports
পাপনের গালে গালে জুতা মার,0,sports
গত বছর শ্রীলঙ্কার সাথেও এমন হইছে। স্পিন উইকেটে নিজেরাই ফাইসা গেছে।,0,sports
প্রবাস থেকে বাংলাদেশের রাজনীতি অস্থিরতা সহিংসতা দলীয় সহিংসতা বিরোধী দলীয় সহিংসতা এসব কিছুই ভাল লাগত না সব সময় চেয়ে থাকতাম বিশ্বের অলরাউন্ডার সাকিব আল হাসানের খেলা দেখার জন্য এবং বাংলাদেশের এতটুকু ভালোলাগার জিনিস ছিল যেটা ক্রিকেট সেটাই আজ ধ্বংস হয়ে গেল,0,sports
বাংলাদেশের সাংবাদিকরা এত অসভ্য এই সংবাদ সম্মেলন দেখেই বুজা যায়,0,sports
বাংলাদেশ একাদশ তামিম লিটন আফিফ নাইম মিটুন সাকিব মুশফিক সাইফুদ্দিন আমিনুল নাইম মোস্তাফিজ,0,sports
বাংলাদেশের ক্রিকেটার রা পাগল হয়ে গেছে,0,sports
আমরা রাজশাহী মামুর বেটা রাজশাহী বুকের বাটা আছে প্রথম বঙ্গবন্ধু নামে বিপিএল টা আমারই জয় লাভ করলাম।,0,sports
ক্রিকেটর নামে দেশের লুটপাট হচ্চে। হারাম খাইতে খাইতে লেজ কাটা কুক্তা হইয়া গেছে।,0,sports
সবাই সাব্বিরের বিরুদ্ধে লেগে আছে কেন বুজি না। সমালোচনার জবাব ব্যাট দিয়ে ভালো করে দিয়েছেন।,0,sports
ভোলাকে ভুলানোর চেস্টা,0,sports
হেডা বন্ধু বিপিএল,0,sports
আসলে আমি একটা কথা বলতে চাই বাংলাদেশের মানুষ হিসাবে। ভুল কিন্তু মানুষেরই হয়। তাই ওই ভুলের সাজা আমরা মানুষকে দেই। তবে আমরা জানি একটা কথা পাপকে ঘৃণা করো পাপীকে নয় ‌। অতএব আমাদের বাংলাদেশের দলের একজন ভালো ব্যাটসম্যান। একটা মানুষের পার্সোনাল জিনিস নিয়ে কেন আমরা তো কথা বলি। এছাড়া এটা দেশের বাইরে মানুষের শুনতেছে।<br />আমরা প্রবাসী। গতকাল একটা ইন্ডিয়ান লোক এসে বলে আমাকে তোদের সাব্বির খারাপ ছেলে।<br />এ কথাটা শুনে ও কে <br /> কিছু উত্তর দিতে পারিনি<br />কেননা আমাদের বাংলাদেশের মানুষ সবকিছু বাহিরে মানুষদের কে বলে দে,0,sports
ভিডিওর সাথে তো টাইটেলের কোন মিল নেই যত্তসব ছ্যাছড়ার দল,0,sports
"হ্যাপি আমি তোমাকে ভালোবাসি,+৩৯৩৫১০৭২১৯৭৯",0,sports
এইসব মিথ্যা খবর নাছড়িয়ে ভিক্ষাকরেখা,0,sports
রনিকে আরও বেশি সুযোগ দেয়া উচিত,0,sports
আবেগ ব্যাবসা অফ করেন,0,sports
"নিন্দুক এর কাজ নিন্দা করা,তাই বলে চুপ করে বসে থাকলে কি চলবে boss",0,sports
কুকুরে তুই মরতে পারিস না,0,sports
সাকিব কি জিনিস পাপন বুঝল না এটা খালেদাজিয়ার মাথা না😂😂।,0,sports
চট্রগ্রাম চ্যালেঞ্জার্সের ভক্তরা কোথায় লাইক হবে👍👍,0,sports
বিসিবি বড় খারাপ এই সব সাজানো নাটক,0,sports
পাগল হয়ে গিয়েছে পাপনেরকোথায় খেলার হিসাব আর কোথায় ব্যাক্তিগত উপকারের খোচা,0,sports
মানি না মানবো না পাপন কে সরিয়ে দেওয়া হক ভোট থেকে,0,sports
ভাই আপনার কথা খুব ভাল লাগলো,0,sports
নতুন একটি নাটক ঘুষ খোর,0,sports
কাঁদিয়ে দিলেন রে ভাই,0,sports
পাপন সাহেব ভুল কি বল্লো এত সমালোচনা করা হবে। পারলে পাপন সাহেব এর কথার যুক্তি যুক্ত উত্তর দেন তার পরে সমালোচনা করে ন।,0,sports
ভাইয়া সাজা তোসাকিব কে দিল না দিল তো বাংলাদেশ কে,0,sports
পাপন সাহেব গরু মেরে জুতা দান করেছেন,0,sports
শালারা ক্রিকেটটা মনে হয় শেষ করে দিবে।,0,sports
যদি আপনারা হাসাহাসি ভিডিও দেখতে চান তাহলে আমার চ্যানেল ঘুরে আসুন,0,sports
ছেলেটা গাড়ি দিয়ে যে অপরাধ করছে তারচেয়ে বেশি অপরাধী হলি তোরা সুন্দর করে বুঝিয়ে দিলে পারতি আজ থেকে মুশফিকের প্রতি ঘৃণা এবার আমাকেও ধরিস আমি তোদের খুনি দেশে থাকি না,0,sports
ভাই পাপনের কেসিনো ভিডিও টা নিয়ে ভিডিও বানান প্লিজ । পাপন কে প্রেসিডেন্ট থেকে বাদ দিয়া হোক,0,sports
ইমরুল বেস্ট,0,sports
বাল ছাল সাব্বির কে পুংগা লাথি দিয়ে বের করে দেয়া উচিত,0,sports
নতুন সৌম্য দেখলাম। 😘,0,sports
রংপুর খুব ভালো,0,sports
রোস্ট টা ভাই আশানুরূপ হয়নি,0,sports
ক্যাসিনো পাপন।।।🤣🤣🤣🤣,0,sports
যারা ঢাকার তারা একটা করে লাইক দিন,0,sports
চুরের কাছে কি জিগাস করো,0,sports
বাংলায়😀😁😀😁,0,sports
খেলা নিয়ে রাজনীতি,0,sports
খুব কষ্ট লাগলো বাংলাদেশ নিজের বিশ্ব সেরা অল রাউন্ডার সাকিব আল হাসান কে হারিয়ে মনের ভাব প্রকাশ করলাম ছোট একটা ভিডিও ভালো লাগলে কমেন্ট করে বুঝিয়ে দেন সাকিব ভাইয়ের প্রতি ভালোবাসা এবং দোয়া,0,sports
ইরেজিতে ভাষা শিখতে পারি না আমি ভাই সেইম আপনার মত।💋❤,0,sports
বিয়াদব,0,sports
আমরা মনে করি সাকিবকে সম্পন্ন ক্রিকেট কাজ থেকে নিষেধ করেছে পাপনের নির্দেশে কেননা আজকে এত বছর হয়ে গেছে কথাটা আইসিসি বলতে পারে নাই আজকে সাকিব দলবেঁধে যখন পাপনের বিরুদ্ধে এবং বিসিবির বিরুদ্ধে আন্দোলন করছিল তখন আপন এই অপমান সহ্য করতে না পেরে সাকিবের উপর প্রতিশোধ নেওয়ার জন্য এই কাজটা করেছে।আমরা ভাই এত বেগোনা আর এত বোকা না যে কোন সময় কি ঘটনা ঘটবে কিসের জন্য কাটাবে সেটা ভালো করে জানে। এমনি সাকিবের পাশে দাঁড়িয়ে মিছে কান্না করলে হবেনা তো আপন ভাই।আপনার নেত্রী যেরকম আপনিও তার থেকে বুদ্ধি নিয়ে ওরকম হয়েছে।,0,sports
দারুণ খবর। অহংকার পতনের মুল।,0,sports
এটা কি উড়িয়ে ই মারলো না পেরেরা,0,sports
আমরা সিলটি ফুয়াইন,0,sports
মেহেদী খুব ভালো খেলে,0,sports
সাকিব আল হাসানের জন্য শুভকামনা রইল ইনশাল্লাহ নির্দোষ প্রমাণিত হবে,0,sports
মমিনুলের ভক্তরা কোথায় লাইক হবে👍👍,0,sports
ভাই এগুলো সব ভুয়া,0,sports
সাব্বিরকে শাস্তি দেয়া ফরয ছিল।,0,sports
পাপোন্দা যদি জানতে পারে। তয়লে আর আপনাকে বিডিতে আসতে দিবে না।অবশ্য এটা দেখার পর ও দেড়মাস পাগল থাকবে 🤔🤔,0,sports
ফিক্সিং হইছে,0,sports
সবাইকেই খেলা দেখতে যাবার জন্য আমি অনুরূধ করিলাম বাংলাদেশে,0,sports
দর্শক দেখে মনে হয় ঢাকার থেকে ভালো চট্টগ্রাম,0,sports
লিটন এর শট যত দেখি তত পাগল হই কোথায় কোহলি কোথাই আজম লিটনের শটই সেরা,0,sports
আহহ সালা একটু লুচ্চা,0,sports
হালার মুচ দেখ,0,sports
পাপোন্দাকে শুধু একটি কথা বলব আমি যে তুই যদি বাপের বেটা হয়ে থাকসতাহলে একবার দর্শকদের কমেন্ট গুলো পড়ে দেখিস।,0,sports
আনন্দ করার মানে কি? এখানে আনন্দ করার কারন দেখিনা। কারন সব দলগুলোর মালিকতো একজনই বিসিবি। দলের মালিকানা যদি আলাদা হতো তাহলে মজা ই হতো।,0,sports
তিন সালা পাগর তাসকিন বড় পাগর,0,sports
আমার দেখা আপনার সবথেকে যুক্তিহীন একটা ভিডিওআর অন্ন্য কে যে আবাল বলেন এই ভিডিওতে আপনি যে বড় আবালের পরিচয় দিছেন এইটা জানেন নাকি😐,0,sports
রাজশাহী সাপোর্টার কেও নাইরে যাক আমি হলাম ইনশাআল্লাহ জিতবে,0,sports
চরম বদমাস..,0,sports
খুলনা প্রতি বছরই নতুন নতুন পেলেয়ার বের করে এ 💟💟💟💟,0,sports
ইমরুল একজন হডহিডার বেছমেন,0,sports
পাপন হাহাহা পাপনদা,0,sports
আফগানীদের কে থেকে ভাত দাও,0,sports
ইনশাআল্লাহ সাকিবের মতো হবে মেহেদী,0,sports
যেই ধরছে অই হালায় এমন বাব ধরছে হেয় হানিনার ভাই,0,sports
সালা পাপ্পন একোন তর পালা।,0,sports
ভাই ঠিক,0,sports
পাপন সাহেব মানুষ এতো খারাপ হতে পারে আপনাকে না দেখলে বুঝাযেতো না আপনি এখন কোটি কোটি মানুষের ঘৃণার পাত্র,0,sports
ভাল করসেন এই রে গালি দিয়ে বাংলাদেশের সব ক্রিকেটের সোজা বাংলা ভাষায় মাদারচোদ,0,sports
নিষেধাজ্ঞায় প্রাপ্ত শাস্তি হ্রাস করা যাবে না?,0,sports
মুশফিক এক জন অনেক ভালো মনের মানুষ তাকে এটা বলা ঠিক হয়নি,0,sports
বাংলাদেশের প্লেয়ারা বিপিএল খুব ভালো খেলেছে,0,sports
প্রধানমন্ত্রীর বাচ্চা কোলে নেওয়াটাও ট্রিটমেন্ট???,0,sports
আন্তর্জাতিক চরিত্রহীন। সানিয়ার জুতাও সাব্বিরের চেহারা থেকে সুন্দর। বিড়াল চোখ দেখলে বমি আসে।,0,sports
যাদের ভুল ধরেছেন তারা কতবছর ধরে ওয়াজ করছে তর ধারণাই নাই শালা।ভুল হতেই পারে কারন তারা মানুষ। আর আজহারীরে এখানে টেনে কি বুঝালি তুই খুব শিক্ষিত ওয়াট প্রুফ বলার পরে এর পরের বার ফায়ার প্রুফ বলছে। আর কিছু বক্সদ মিনিটের বক্তব্য শুনে যারা হুজুরদের গালি দিচ্ছেন আল্লাহ তাদের হেদায়েত দান করুক,0,sports
সব নাটের গুরু পাপন তার গোপন তথ্য ফাঁস হয়ে যাবে এজন্য এই নাটক করতেছে পাপন,0,sports
সাকিব ও বাংলাদেশ কে বাচাও পাপন কে হটাও😑😑😑,0,sports
আমি আর কোন কারনে কান্না করি না আজ অনেক কান্না পাচ্ছে বাংলাদেশ এর খেলা হোক আইপিএল সিপিএল যত লীগ যাই হোক সাকিব কে লাগবেই গিয়ে দেখেন সব ফরমেটে বেস্ট অল রাউন্ডার অকে ছাড়া বছর বাংলাদেশ ক্রিকেট অনেক নিচে চলে যাবে,0,sports
সবাই তো আর আপন হয়না কিছু কিছু মানুষ কুত্তার বাচ্চা পাপন ও হয়,0,sports
রাজশাহী নিবে কাপ,0,sports
শোয়েব মালিক তোর বাপের চেয়ে বয়সে বড় শালা। শোয়েব যদি সঠিক বয়সে বিয়ে করতো তাহলে তোর মতো ছেলে থাকতো।,0,sports
সাকিবে এমন কান্না বরা মুখ আর কখন ও দেখিনি বাংলাদেশ প্রদানমন্তি আপনি পাপনকে বিসিবি থেকে সরিয়ে দিন না হলে বাংলার টাইগাররা সুজা হতেই পাপন হাটু ভেঙ্গে দিবেতাই আপনার কাছে রিকুয়েষ্ট সাকিব ভাইকে অবসর না দিয়ে আবার ফিরিয়ে আনোনআপনি দেখেন আসরাফুল একজন ভালো খেলুয়ার ছিলো তাকে এখনও আনা হয়নিআর কত প্লেয়ার হারাবে বাংলাদেশ,0,sports
আপনার সাথে সহ মত,0,sports
পুলিশ এখানে কি করে আমি বুজিনা,0,sports
বিসিবির সভাপতির পদত্যাগ চাই জাতি,0,sports
ভাই আপনি সবাই বুঝতে পড়ে না।আপনি বুঝতে পড়ে ছেন।,0,sports
বোকার দল মুশফিক গোষ্ঠী উদ্ধার করলে কোন খাবার ধান্দা,0,sports
বাংলাদেশ টা চলছে এখন ধোকাবাজ এর উপর,0,sports
হালা আবাল। কিছু না জেনেই ফালতু নিউজ ছড়াস কেনো?,0,sports
আশরাফুলকেত গেল এবার সাকিব,0,sports
দেব চৌধুরী ছাড়া কি আর কোন সাংবাদিক নাই ক্রিকেটে এর নিউজ কাভার করার জন্য,0,sports
তামিম ইকবাল বস,0,sports
সাদা গেন্জি গায়ে জে কথা বলছে সে আমার কাকু হারুন অর রশিদ,0,sports
আসালামু আলাইকুম 👍👍👍👍👍👍👍🌸🌸🌸🌸🌸🌸,0,sports
বাংলাদেশে এর আভাব নেই একটা শেষ হতে না হতে আর একটা শুরু হয়ে যাই।,0,sports
পাপন ভাই আর যাই হোক একটা সত্যি কথা বলেছে। আর তা হলো ক্রিকেট নিয়ে বাহির থেকে কেউ খেলছে। আর পাপন ভাইসুজননান্নু কে সরাতে হবে। আর আমিনুল ইসলাম বুলবুলকে নেক্সট কোচ করতে হবে,0,sports
র,0,sports
আলহামদুলিল্লাহ যাক সেস বেস রাজশাহী বিজয় হইলো স্বচ্চ অবোদান দিয়েছে আন্দে রাসেল তানা হলে রাজশাহী ফাইনালে আসতে পারতো না আশা করি রাজশাহী মানুষ আন্দে রাসেলের প্রফারমেঞ্চ কখনো ভুলবেনা,0,sports
একটা লজিক্যাল কথাও এখানে নাই। আছে শুধু নুর ভাইয়ের প্রতি ক্ষোভ ঘৃনা। মনে হচ্ছে একটা উদ্ভ্রান্ত শুয়োর হাকডাক করে বেড়াচ্ছে। ইউটিউব টা আজ খুব সস্তা হয়ে গেছে গাজাখোররা একটা ক্যামেরা ম্যানেজ করলেই নিজেকে ইউটিউবার ভাবা শুরু করে দিচ্ছে,0,sports
বাংলাদেশের পিলিয়ারের মাঝে এখন লোভ জেগে গেছে বিসিবি পাপন ভাইকে বলছি এই সব দোষ আপনার আপনি না বলতেই বেতন বাড়িয়ে দিয়েছেন এই টাকা কোথা থেকে আসে আমাদের সরকারি আয়ের কিন্তু ওনারা কোন একদিন একটি বড় কাপ জিতে দিয়ে দেয়নি আর কোনদিন দিতে পারব না কারণ তাদের মাঝে লোভ জেগে গেছে তাদেরকে যত টাকা দেওয়া হবে তাদের পেট ভরবে না আমি যদি কোনো ভুল বলে থাকি তাহলে আমাকে ক্ষমা করবেন,0,sports
বালের ভিডিও! এইটা কোনো উইনিং মোমেন্ট হইলো? তাড়াহুড়ো করে উইনিং মোমেন্ট বাদ দিয়ে দিসো যে নিজেই জানোনা!,0,sports
ইন্ডিয়া সিরিজ থাকার একমাত্র কারণ সাকিব,0,sports
সৌম্য সরকার,0,sports
আসলে উনাকে বহিষ্কার করাটা অনেক দরকার উনি পুরো ক্রিকেট দলকে ধ্বংস করতে যাচ্ছে শুধু সাকিবকে না যেমন আশরাফুলকে ধ্বংস করে দিল এরপর উনার মেয়ের সাথে প্রেম করার অপরাধে নাসিরকেও বিভিন্ন অজুহাত দেখিয়ে বাদ দিয়ে দিল,0,sports
বাজে,0,sports
সাকিব না খেল্লে কারা কারা খেলা দেখবেন না লাইক দিয়ে প্রতিবাদ করুন👇🏿,0,sports
ভাই চামচা গুলার এইরকম করার কারন টাকা আর কিছু নাহ,0,sports
ইন্ডিয়া বাংলাদেশকে কখনোই আগাতে দিবে না আর সেই ক্ষেত্রে আমাদের কিছু নাম ধারি বাংগালী দেশে বসে হেল্প করে ইন্ডিয়ান দের,0,sports
পাপনের পদতেক চাই,0,sports
ভাই গার্লফ্রেন্ড কষ্ট দিলে যেরকম কষ্ট লাগে তার চেয়ে বেশি কষ্ট লাগছে আছ,0,sports
টস জিতার পর ধারাভাষ্যকার প্রতিটি ম্যাচে নিজে বলেদেন না করতে,0,sports
ভালোবাসার মানুষ যেখানেই থাকুক ভালো থাকুক বাংলাদেশের না হয় ইংল্যান্ডের হয়ে গেল তারপরও সে ভালো খেলো আমাদের দোয়া রইল কারণ আমরা তাকে ভালোবাসি তার খেলা কে ভালবাসি আর বাংলাদেশের মধ্যে থেকে সাকিবের মত এবং কোন ভাল মানুষের তাই আমাদের বাংলাদেশে নাই সেটাই আমরা প্রমাণ করলাম আমাদের সাকিবের জন্য অনেক দ্রুত হয় এবং দোয়া রইলো সাকিব যাতে যেখানে থাকে ভালো থাকে,0,sports
এই রকম একটা সৎ এবং প্রতিভাবান খেলোয়াড় কে ওরা কিভাবে বহিষ্কার করতে পরেএটা চক্রান্ত করা হয়েছে ভাই এর বিরুদ্ধেআজ হইতো সাকিব কাদে নিকিন্তু কেদেছে তার অন্তর আত্মা ।বিনা দোষে আজ সে দোষী 😔😔😔😰😰,0,sports
সাব্বির একটু উগ্রবাদী এটা সবাই জানে কিন্তু প্রশ্ন হল ৫ বছর আগের ইস্যু টা ৫ বছর পরে ক্যান হল!অবিয়াস্লি এটা অপরাধ তাহলে যখন অপরাধ টা করছিলো তখন শাস্তি না দিয়ে এতদিন পর ক্যান এটা নিয়া ঘাটাঘাটি??,0,sports
মমিনুল কে সব ফরমেটে নেয়া উচিত,0,sports
ওয়ান্দ্রআরফুল,0,sports
তদন্দ করে তো জানাই গেলো ছেলেটা গালি দেয় নাই আর মুশফিক ভাই ও ওকে কিছুই বলে নাই খালি খালি এই শালারা এই ছেলেটার সাথে অবিচার করলো 😡,0,sports
মেহেদী হাসান রানা এগিয়ে যাও,0,sports
"মাহাম্মাুদুল্লাহ, মাশরাফি আর মুশফিকুর বাদে বাংলাদেশ জাতীয়দলের সকল খেলোয়াড় কম-বেশী খারাপ।",0,sports
গেছে ক্রিকেট খেলা গেছে বাংলাদেশের,0,sports
পাপন দা খুশি,0,sports
অনেকদিন পর ভুতার ব্যাট চলছে,0,sports
বাংলাদেশ ক্রিকেট দল শেষ,0,sports
পাপন একটা পাগল,0,sports
ব্যাপার নাহ ভাই..মেয়েই তো,0,sports
এরকম বিকৃত মানসিকতার লোক কখনোই বাংলাদেশ দলে না আসুক।,0,sports
মোহাম্মদ নাবি কে অধিনায়ক না করে দেশি কোন প্লেয়ার কে অধিনায়ক করা দরকার।,0,sports
সাকিবের বিসিবি র সাথে শত্রুতা থাকলেও দেশের মানুষ আজ ও তাকে ভালোবাসে । সাকিবকে এটা ভাবা উচিৎ।,0,sports
সাকিবের উচিত ক্রিকেটকে বিদায় জানানো তাহলেই বুঝবে সাকিব কি ছিলো দলের জন্য।।কলঙ্কিত হয়ে ক্রিকেট খেলার থেকে না খেলাই ভালো।।,0,sports
অসাধারণ বল❤️আমির,0,sports
অভিনন্দন রাজশাহীবাসী । মন খারাপ করোনা খুলনাবাসী । কেউ জিতে কেউ হারে এটাই নিয়ম। আমরা যে এতদুর এসেছি এটাই অনেক খুশির ব্যাপার। ধন্যবাদ মুশফিক।,0,sports
ধন্যবাদ ভাই প্রতিবাদ চালিয়ে যান,0,sports
তামিম ইকবাল শুধু বাংলাদেশ নয় বিশ্বের সেরা টি টুয়েন্টি ব্যাটসম্যান😂😂😂😂😂,0,sports
তাসকিন রে দুই ডা মার হালায় বুজুক কেমন লাগে বইসা বইসা মজা দেখে হালায় রে ও মার,0,sports
পাপন সাহেবের জায়গায় মাশরাফি কে দেখতে চাই। এবং অবশেষে এমনটাই হতে যাচ্ছে।,0,sports
পাপোন্দা হাঁটাও ক্রিকেট বাচাঁও!!!,0,sports
কি এডিটিং করেন এসব! এক নো বল এর হাইলাইটস দেখান মিনিট ধরে।,0,sports
এখানে যারা কমেন্ট করতেছে তাদের মাথায় দেখতেছি আসলে গোবর ছাড়া কিছুই নেই।। এক একটা যেন মদ খাইয়া কমেন্ট করতেছে। বুজে না বুজে সব উলটাপালটা কমেন্ট করতেছে,0,sports
তাহসিন ভাইর ভিডিও ভালো লাগে এই জন্যে কথাগুলো যুক্তিযুক্ত ভাবে ফুটিয়ে তোলেন🥰,0,sports
আমার মনে হয় এইটা বুঝাতে চাইছে ওনি,0,sports
নবীকে গালি দিলে বিচার হয় না সমান্য মানুষ মুশফিক কে কি যেনো বলছে এতো তোলপার,0,sports
আমার মনে হয় এটা পাপনের হাত আছে,0,sports
পাপন থাকলে বাংলাদেশ ভালো পর্যায়ে যেতে পারবে না বরং আরো নেমে যাবে,0,sports
ছাব্বিরের নুনু কেটে ফেলে দেয়া হুক তাহলে ভালই হবে,0,sports
মুশফিক আমার বগুড়ার পোলা রে কাপটা পাইলো না তার জন্য অনেক কষ্ট পাইছি। তারপর রাজশাহী জিতছে এটাতে খুশি আমি😁😁,0,sports
বস্তির ছেলে যখন পয়সার মুখ দেখে,0,sports
পাপনের মুখে মুতে দাও,0,sports
এদের কে ভালোবাসা বেশি হয়ে গিয়েছে।,0,sports
বাংলাদেশ ক্রিকেট দল গতকাল থেকেই শেষ হয়ে গেছে।,0,sports
সাকিবের জায়গায় পাপনদা খেলবেচিন্তা কিসের,0,sports
বাংলাদেশের ক্রিকেটটাকে পাপন ধ্বংস করবো এখন এটার ভিতর পাপনের এবং ভারতের হাত আছে বাংলাদেশের ভাই ও বোনেরা আপনারা এটা বিশ্বাস করেন এটার পিছনে বাপনের হাত আছে নিশ্চিত এবং ভারতের হাত আছে,0,sports
মোনের কথা বলেছো দাদু তোমাকেই বিসিবি সভাপতি হিসেবে চাই,0,sports
হেপি তুই বিষ খা কারো বউ হওয়ার যোগতা তোদের নাই,0,sports
কৃষক কৃষক লাগে।,0,sports
লিটু😘,0,sports
শান্তকে জাতীয় দলে।যে কয়বার আনলো ততো বার ডাক মারছে,0,sports
সুরা বাকারার নাম্বার আয়াতের আল্লাহ ধর্মব্যবসা নিষিদ্ধ করেছেন আবং আগুন খাওয়ার সমতুল্য করেছেন ধর্মব্যবসায়ীরা ওয়াজ করে হারাম উপার্জন চালিয়ে যাচ্ছে এটা তো হারাম উপার্জন এখনো সময় আছে ধান্দা বাচ্চাদের বয়কোট করুন।,0,sports
ওই সালা তাই আসরাফুল মারা গেছে,0,sports
ভাবতেই অবাক লাগে! নাম্বার জার্সি পরিহিত বিশ্বসেরা অলরাউন্ডারকে টি বিশ্বকাপে দেখতে পাবো নাখুবই মিস করবো,0,sports
সাকিব তোমাকে ভালবাসি সারা জীবন ভালোবাসবো 🇧🇩🇧🇩🇧🇩❤❤❤,0,sports
সাকিব ভাই ছাড়া বাংলাদেশ একদম দুর্বল,0,sports
এই রকম মজা কইরেন না যাতে একটা মানুষ মনের মধ্যে কষ্ট পাই,0,sports
দালালের দল বাংলাদেশ এটাই তো হবে,0,sports
আমি তো আজ শুনলাম এর কথাজানতাম পাপন আর বিসিবি;ই এই কাজ করছে।। ওদের সম্মেলন এর থাম্বনেইল দেখে তো তাই মনে হয়।,0,sports
এট া কোন কথা 😡 একটা নিরিহ ছেলে কে কেনো এত হয়রানি করলো। 😡 সামান্য একটা বেপার নিয়ে !!,0,sports
এই শালার পুতেরা আমার বাল সাল কইছে বেকার ছেলেটারে হয়রানির করতেছ! ছেলেটায় বার বার বলছে গালি দিছে না তারপর ও তাকে হয়রানি করছ!এই হল আমরা বাংগালী!,0,sports
চোরের নেতা জয়নাল এটি একটি নাটক সবাই দেখবেন প্লিজ,0,sports
একটা কথা খেলোয়াড়রা শুনতে হবে কেন আপনারা কোটি কোটি টাকা লাখ লাখ টাকা কামাচ্ছেন আপনাদেরকে একজন একটা কথা বলতে পারবে গালি দিলে সেটা আপনি প্রতিপাদ্যের বেন্নগালি যদি না দেয় অতিরিক্ত কোনো কথা বললে প্রতিবাদ করবেন না ধন্যবাদ আপনি অনেক বাংলাদেশের ভালো খেলোয়ার অনেক ভালো এখন আস্তে আস্তে বন্ধ হয়ে যাইতেছে,0,sports
ধ্বংস ধ্বংস সব ধ্বংস করে দিলো 😢😢😢,0,sports
কে ফোন করে কি অফার করেছে তাতে কি যায় আসেশাকিব তো রাজি হয় নিতার অপরাধ কি?সে বলেনি এটা? বল্লে কি করতো এতো পারে এখন কেন জোয়ারো কে দরেনা,0,sports
তাসকিন অনেক খারাপ,0,sports
হিসাবটা খুব সহজ।ভারত সফরের আগে সাকিবকে বাদ দিলে বাংলাদেশ দল দূর্বল হয়ে গেল।বেয়াদব বাংলাদেশ যে এখন ভারতকে চ্যালেন্জ জানায়!এদেরকে সাইজ করতে হবে না!?আর পাপনরাতো পেয়ারে ভারত!,0,sports
ভাই পাপন বাংলাদেশ ক্রিকেট টিমকে ধ্বংস করতে চাচ্ছে।,0,sports
এটি একটি নাটক সবাই দেখবেন,0,sports
আসসালামু আলাইকুম মুসলিম ভাই ও বোনেরা,0,sports
গুড,0,sports
হালা নিউজ ।।।।।,0,sports
"এখানে বেয়াদবি কিছু দেখছি না। একটা ছেলে জাতীয় দল থেকে বাদ পরে আবার টিমে ফিরে রান করছে।সাব্বির বলতে চেয়েছে তার ব্যাট আজ রান করেছে মানে কথা বলেছে। সাব্বির পেরেছে আস্থার প্রতিদান দিতে <br />ব্যাট ও হাত দেখিয়ে ড্রেসিং রুমের দিকে ইশারা করে এটাই বলতে চাইছেন সাব্বির। সাব্বির বলেছিলেন, নিউজিল্যান্ডে তার ২য় অভিষেক হবে।",0,sports
খুব মজা পাইলাম।,0,sports
কাটারের আবার ছন্দে ফিরে এসে পড়েছে৷ ❤💙💋💯,0,sports
হালারে মুলার জুস খাওয়া,0,sports
মানিব্যাগের মোবাইলটা নেওয়ার নেওয়ার জন্য এত কাজ করছে গাঞ্জাখোর,0,sports
যারা বাজে মানুষ যাদের লজ্জা বলে কিছু নেই তারা নুংরা কমেন্ট করেছে।নাসির ভাই মনে কষ্ট নিবেন না আমরা আছি আপনার সাথে,0,sports
আমার বুঝে আসেনা একজন ক্যাসিনো প্লেয়ার ! কিভাবে এখনো বিসিবি,0,sports
বাংলাদেশ এবার জিম্বাবুয়ের মতো হতে আর বেশি দেরি নাই,0,sports
আর কত দুনীতি করবে রে। একদিন পতন হবে। ইনশাআল্লাহ,0,sports
সময় থাকতে কল করেন ধান্দা বাজদের কথাই জীবন আন্ধা হবার আগে কল করেন,0,sports
সাকিব এক বছর বউ নিয়ে ঘুরে বেড়াতে পারবে।শাস্তিতে সাকিব খুব খুশি।,0,sports
মির্জাফর পাপনকে হঠাওদেশের ক্রিকেট বাঁচাও!ঘটনাটি বছর আগের যেটা পাপনের আগে জানা ছিলকিন্তু কখনো বলা হয়ে উঠেনি সাকিবের সাথে তখন সমঝোতা ছিল বলেএখন কেন হঠাৎ বলতে বাধ্য হল কারণ দফা দাবির আন্দোলনে সাকিবের নেতৃত্বে জিতে যাওয়াতে কোনো উপায় না পেয়ে বছরের আগের কথা দিয়ে শাস্তি দিল!,0,sports
হ্মতি হবে,0,sports
জনগনের পাছায় নাথি মারার দরকার বোকাচুদারা প্লেয়ারদের পিছনে লাগছে কেন এত মানুষ রেখে সালাকে কেউ পাঠায়ছে,0,sports
নষ্টামি ছারা আর কিছুই না হে আল্লাহ ত্রগূলিকে হেদায়েত দান করুন আমিন,0,sports
আমাদের কক্সবাজারের গৌরব,0,sports
অসাধারন লাগলো আমিত ভাই😊😊😊,0,sports
সালা চুর,0,sports
কেন ভাই?? কেন?????একই তোহ ভিডিও সবার শেষে আপ দিচ্ছেনতার উপরে আবার এত্তো বড় ভিডিও🤔🤔এইগুলা আপনার কাছে আশা করিনাই😑,0,sports
প্রতিটা ম্যাচেই সৌম্য সরকারকে এমন রুপে দেখতে ইচ্ছা করে ❤❤ সৌম্য ❤❤ 🇧🇩🇧🇩🇧🇩,0,sports
খুব সুন্দর কথা বলেছেন ভাই আপনি,0,sports
রাজস্থান রয়েলস কত্থেকে আসলো,0,sports
পাওল খবর,0,sports
অনেক ভালো কতা বলেন পাপন,0,sports
সবই পাপনের কাটসাজি,0,sports
জুতা মারো তালে তালে পাপনের দুই গালে,0,sports
দুষ্টু লোকের মিষ্টি কথা। এমন ভাবে বলেছেন যেনো সব দোষ ক্রিকেটারদের। আচ্ছা এতদিন ধরে যদি সবকিছু বলার সাথে সাথেই যদি মনে নিয়েছেন তাহলে সবাই মিলে আন্দোলন করবেন কেন। আমি বুঝতে পারলাম না। আচ্ছা তাহলে মিডিয়ার কাছে প্রমাণ করান।🤔🤔🤔🤔🤔🤔🤔🤔🤔🤔🤔🤔🤔,0,sports
তাসকিন না,0,sports
মেহেদি খুব ভাল খেলছে তার জন্ন্য লাইক হবে,0,sports
শুধু মাত্র চট্টগ্রামের ভক্তরা লাইক দাও,0,sports
পাপন সাহেবকে বোর্ড থেকে বাদ দিতে হবে,0,sports
ওর মতো ক্রিকেটার বাংলাদেশে কোন প্রয়োজন নেই।,0,sports
অনেকেই অনেক কথা বলছে।ভাই ইংরেজি বললে কয়জনে বুঝে। আমার মতে দেশের ক্রিকেটাররা দেশিও খেলায় বাংলা বললে ভালো হয়।বিদেশে খেলা হলে তখন না হয় ইংলিস বলবে।,0,sports
কেন যেন ঢাকার খেলা ফিক্সিং মনে হলো,0,sports
এবারের বিপিএলের সেরা ম্যাচ এটাই । অভিনন্দন আন্দ্রে রাসেল ফাইনালে ।,0,sports
"সানিয়া মির্জা হলো একটা মাগি,আর তুই সাংবাদিক হলি একটা মাগিরপুত,সালারপুত নিজের দেশের হোগা মারার জন্য উঠেপড়ে লেগেছিস, এটা ওদের দেশে হলে তোদের চোদতো ওইখানে,রিপোর্ট চোদাচ নিজের দেশের নামে,খানকিরপোলা",0,sports
পাঠা একটা ❤,0,sports
বঙ্গবন্ধুর প্রেতাত্মা কে ধরে নিয়ে আসা হইছে ওপার থেকে বিপিএলের ফাইনাল দেখতে বঙ্গবন্ধুর প্রেতাত্মা এখন কাউয়ার উপর ভর করে কাউয়ার রূপে আমাদের মাঝে আমরা সবাই স্বাগত জানাই ভবিষ্যতে আশাকরি দেশের পাবলিক টয়লেট গুলিও বঙ্গবন্ধুর নামে করে সেখানে বঙ্গবন্ধুর উপস্থিতি নিশ্চিত করবে তার তাজাজ্জুদি কন্যা বঙ্গবন্ধুর জন্মশতবার্ষিকী উপলক্ষে আমি ইতিমধ্যে আমার কমডেও একখানা বঙ্গবন্ধুর ছবি লাগাইছি হাগতে বসলেই দেখি আর ভাবি কত সৌভাগ্যবান আমাদের বঙ্গবন্ধু! আর কত দুর্ভাগা জাতি আমরা !!! এক বঙ্গবন্ধু মইরাও সালা মরে না! আর এক আমরা হাগতে বইয়া ভাবতে হয় বঙ্গবন্ধুর কথা 🤔,0,sports
মুশি ভাই সত্যি অসাধারণ মেধাবী একজন ক্রিকেটার। সময় অনুযায়ী খেলে যেতে পারে।।।স্যালুট বস,0,sports
"বিয়ের আগে বউ-স্বামীর মত চলাফেরা করবেন,আবার বিয়ের প্রস্তাবে রাজি না হলে নির্লজ্জের মত রেডিও-টিভিতে প্রকাশও করবেন!!!<br />কেন???দেহ দেওয়ার আগে একবারের জন্যও মনে পড়েনি যে ছেলে আপনার সাথে এমন<br />পাপাচারে লিপ্ত সে হয়ত আপনাকে ছেড়ে চলেও যেতে পারে অন্য কোন দেহের লোভে?<br />সে ছেলের কিসের বিচার চাচ্ছেন??? কোন অপকর্মের জন্য??? কি আপনার সাথে প্রতারণা করার জন্য ???<br />সে প্রতারণা তো আপনিও করতেন যদি অাপনার কাছে পাপাচারী ছেলেটি থেকে ভাল<br />অপশান থাকতো । কি প্রমাণ চান??? মিস.প্রভার কথাই ভাবুন;প্রভা যে ছেলের সাথে অপকর্ম করেছে সে ছেলে থেকে বেটার অপশান অপূর্বকে মনে করেছে বিধায় পাপাচারী ছেলেটি ছেড়ে অপূর্বকে বিয়ে করেছে।<br />আমাদের সমাজে এমন অনেক প্রেমিক-প্রেমিকা দেখা যায় যারা এমন অপকর্ম করে বেড়ায়।পরে উপায় না পেয়ে কেউ নিভৃতে কাঁদে কেউ আত্নহত্যা করে। এসব ঘটনার কিছু তথ্য মিডিয়াতে আসে বাকী সব ঢাকা পড়ে যায় ।<br />পাপাচারীদের এমন কৃতকর্মে তারা কখনও নিজেরা কাঁদে,আবার কখনও তাদের নির্দোষ স্বামী বা স্ত্রীকে কাঁদায়।<br />সুতরাং অপরাধ যেভাবেই ঘটুক যার প্ররচণায় ঘটুক ।দুজনই অপরাধী।<br />বিচার হোক দুজনেরই।।।।",0,sports
খুশির সংবাদ আজকে মিজানুর রহমান আজহারি হুজুরের ওয়াজ মাহফিলে লাখ মানুষ হয়েছে।,0,sports
ক্ষমা চেয়ে ভুল স্বীকার করছে সেটাও দেখে দেখে বলতে হচ্ছে!!! মন থেকে শব্দ আসছেনা। অদ্ভূত!,0,sports
ম্যাচ ফিকচিং করার কোনো দরকার ছিলো না রে ভাই,0,sports
কি খেলা দেখাইলা রাসেল ব্র 😎😎 রাজশাহী চলে গেলো ফাইনালে🤪🤪🤪 ঢাকা তুমি অপেক্ষা কর আসতেছি আমরা 👹 খেলা হবে ফাইনালে🤜🤛,0,sports
মুস্তাফিজুর রহমানের ভক্তরা কোথায় লাইক হবে👍👍,0,sports
সাকিব ছারা বাংলাদেশ টিম অচল কে কে মনে করেন হাত তুলেন।,0,sports
রাসেল এর ব্যাটিং কার কার ভালো লাগে?? লাইক দাও,0,sports
পাপন হচ্ছে একটা লোভি,0,sports
কি বলবো ভাষা খুজে পাচ্ছি না।খুবি বাজে অন্ষটান,0,sports
বিশ্বের 🌍সেরা স্মার্ট 📱ফোনগুলো সম্পর্কে জানতে ঘুরে আসুন আমাদের চ্যানেল🎁 থেকে। মজা পাবেন সিউর। মজা না পেলে টাকা📱 ফেরত। কথা দিলাম।।,0,sports
আমাদের মতন টাইগার সমর্থক গোষ্ঠীদের একটাই দাবি জুয়াড়িদের বিসিবি থেকে বের করে দেওয়া হোক,0,sports
পাপন নান্নুকে পদত্যাগ করতে হবে জলদি,0,sports
আমি ও ঘোষনা দিয়েছিসাকীব বিহীন জাতীয় দলের খেলা আর দেখব না।ধন্যবাদ।,0,sports
একদন ফালতু কথা,0,sports
এর বিচার করবে আললাহ্ মনে রাখিস রুবেল এটাই তোমার শেষ দুনিয়া না,0,sports
মাগি,0,sports
পাপন নাশক মেডিসিনে সাকিব বিদায়।।।।,0,sports
আমার কাছে মনে হচ্ছে বিপিএল এইনিয়মে এই ভাবে করা দরকার ।প্রতিটি বারের চেয়ে এই বার দেশি খেলোয়াড়রা খেলার বেশি বেশি সুযোগ পেয়েছে অনেকে ভালো খেলেছে ।,0,sports
হুম সালাই জড়িতো,0,sports
হাসিনা। অবৈধ,0,sports
সাকিব ভাই ছাড়া বাংলাদেশের টিম অন্ধ। যার কারণে বাংলাদেশকে বিশ্বের মানুষ ছিনে আর থাকেই নাকি খেলা থেকে বাদ দেওয়া হয়ছে। আফসোস আর ভাই আপনি অনেক সুন্দর কথা বলেছেন,0,sports
সব সমস্যা মূল হল দিনের ভোট রাতে হলে আইন থাকে কোথায় বিচার কে করবে আল্লাহ তুমি জানোয়ার দের হাত থেকে দেশকে বাঁচান,0,sports
পাপন কে কে কে জুতা দিয়ে পিঠাতে চাও আমার সাথে যোগ দাও,0,sports
সাব্বির কে? 🤔,0,sports
আমাদের দেশের অনেক মানুষ আছে জে কেই জদি ভালো কিছু করে তাঁকে কি ভাবে বাঁস দেয়া জাই সেই তালে থাকে,0,sports
সাব্বাস বাঘের বাচ্চা 😃😁😀😂😂😂😂😢,0,sports
আরে সাকিব ভাইয়া তোমাকে সেলুট তুমি কি আমাদের কে বুলে জেওনাতোমাকে ভালোবাসি,0,sports
সাকিব আল হাসান এর স্টাইল 😍😍,0,sports
কি তাসকিন ভাইয়া তুমিও পানি করতেছ,0,sports
ছি এইটা কোন ধরনের খেলা? তাসকিন ভাইয়া কেন তাদের বাধ্য করলেন এইসব করতে,0,sports
মাঠে এতো দর্শক গেলো কেমনে,0,sports
চামচামি দিন থাকবেনা আজ তোর দিন কাল হয়তো তার দিন,0,sports
বাংলাদেশ ক্রিকেট অনেক এগোবে প্রত্যেক ভারতবাসী সেটা চায়। কিন্তু তার আগে তাদের ফ্যানদের একটু অহংকার কমাতে হবে। ভারতের সাথে তাদের কি শত্রুতা তা জানিনা। প্রত্যেক ভারতবাসী বাংলাদেশের সাফল্য চায়। ফ্যানদের একটুও অহংকার কমাতে হবে ফ্যানদের,0,sports
ভাই আমি আপনার পেন আপনাকে আনেক আশা নিয়ে কথা বলতেছি কে আরেক বার এমন ভাবে করেন যেন তার কমে যায় ভাই 🙏🙏,0,sports
গেইল এন্ড রাসেল আজকে দেখিয়ে দিলো,0,sports
হাইলাইটস এত্তোবড় হয় ক্যান?,0,sports
আরাফাত সানি ছিল ওকে কি জন্য বল দিল না বুঝলাম না আর গেগরি কোন বলার বালের অধিনায়ক ওভারে সুন্দর বলিং,0,sports
পাপে পুর্ন পাপন। চেহারায় প্রকাশ পায়। ক্রিকেট ধংসের পথে নিয়ে যাচ্ছে।,0,sports
পাপন সাহেব কে চেঞ্জ করা হোক তা হলে সব ঠিক হয়ে যাবে,0,sports
চালিয়ে যান। আপনাদের এক হয়ে এখন মুখ খোলা দরকার।আমাদের মধ্যে অনেক বড় একটা অংশ এদের দ্বারা হিপনোটাইজড। এই ভন্ডদের এক্সপোজ করার সময় এখনই।,0,sports
রাসেলের কারনে অনেকের কপাল পুড়েছে।রাসেল অনেক অনেক ভালো খেলোয়ার। অভিনন্দন রাজশাহীকে।,0,sports
এই রকম বিসিবি কে আমরা চাই।।। সবাই কে একটু গরম করে দেন।,0,sports
একটা জিনিস লক্ষ্য করলাম যে টিমে রাইলো রুশো থাকে সেই টিমই ভালো অবস্থানে থাকে😍,0,sports
মাইরে কি শট রে বাবা 😍😍😍,0,sports
মেহেদী হাসানের ভক্তরা কোথায় লাইক হবে👍👍,0,sports
এমন কিছু হবে সেটা আগেই পাপন সাহেব ঈগিত করেছেন,0,sports
ভাই বুকটা ফেটে যাচ্ছে,0,sports
ইন্ডিয়াই জুয়াড়িদের স্বর্গরাজ্য। আমার ভারতের একটা দলই আছে যারা ভালো ভালো খেলোয়ারদের সাথে কোনক্রমেই যুক্ত করেই খেলোয়ারদের ক্যারিয়ার নষ্ট করে দিচ্ছে।আর এদের প্রধান টার্গেট পাকিস্তান ও বাংলাদেশের খেলোয়ার।আর আমার মনে হয় আই সি সি ও এর সাথে যুক্ত। কারণ তারা শাস্তি শুধু খেলোয়ারদের দিচ্ছে। কিন্তু যারা এর সাথে যুক্ত তাদেরকে গ্রেফতার করছে না।,0,sports
আপন মানুষ পাপন হলেই একজন যোদ্ধা হেরে যায়,0,sports
সাব্বিরকে দল থেকে বের করে দেয়া হোক,0,sports
ছি ছি কি লজ্জা।,0,sports
শিরোপা টা বাংলাদেশের মুশপিক ভাইয়ের কাছে গেলে খুশি হতাম,0,sports
চাপা,0,sports
মানুষের চরিত্র কাল্পনিক অস্তিত্বগুলো হার মানায় যুদ্ধক্ষেত্রের,0,sports
হালারে আনসাস্ক্রাইব কইরা রিপোর্টে মারেন সবাই,0,sports
মাসরাফি বাল ফালাইছে,0,sports
এই দরেন খুশিতে ঠ্যালায় ঘোরতে।,0,sports
আমার মনে হয় যে সামনে ইন্ডিয়ার সিরিজ তাই পাপন কে দিয়ে ইন্ডিয়া য়ে কাজ করিয়েছে যাতে করে ইন্ডিয়া সিরিজ জিততে পারে এর কারণ যে বিরাট কুলি সহ আর কয়েক জন প্লেয়ার রেষ্টে আছে তাই ইন্ডিয়ার জন্য সিরিজ কষ্ট হবে জিততে আমি সিওর যে ইন্ডায়া সিরিজ শেষ হবার পর সাকিবের নিষেধাকা টাইম কমে আসবে কালকে পাপনের বক্তবে বুঝা গেল পাপন বল্ল যে আমি আমার বিসিবি সাকিবের পাশে তাকবে পাশে যদি তাকার ইচ্চা হত তাহলে ইন্ডায়া র সিরিজ পরে কে বল্লে তারা রাজি হত পাপন সুন লাম যে কি করমর্তা আমি বলব যে পাপন কে হাত করে ইন্ডায়া এ কাজ করেছে আমি চাই না আমি নায় সাবাই চাই পাপন আপনার বয়স নাই সভাপতি করার আপনি অবসর নেন ক্রিকেট কে দূরনীতি মুক্ত করুন দয়া করি আমার এই পোষ্টটি পড়বেন,0,sports
পাপন্দার সিলেট থান্ডার ম্যাচে জয় হার পয়েন্ট টেবিল ওরা এখন কাপ নিয়ে চা বাগানে পালাইছে এই শীতের চোদনে তাদেরকে আর পাওয়া যাচ্ছে না,0,sports
বালের খেলা চলে ঢাকায় টা দর্শক নাই মাঠে! শালার ঢাকায় মানুষ খাবার খাইতে পাইনা আবার খেলা ও দেখবে,0,sports
কুওা,0,sports
সাকিব একজনই আর কোন সাকিব জন্মাবে না,0,sports
দেশের জন্য যে মানুষটা খেটেছে অমলান❤চোখের সামনে তারই আজ গঠেছে অবসানহায়রে বাংলাদেশ হায়রে মানুষ সত্যের বিজয়ের অপেক্ষায় আছি সাকিব ভাই,0,sports
ক্রিকেট খেলা বাই বাই ভালো থেকো সাকিব৷ আর খেলা দেখা হবে না।,0,sports
রাজশাহী দল কে রাঙ্গামাটি পক্ষ থেকে অভিনন্দন জানাছি আশা করি ফাইনার ও রাজশাহী জিতবে😍😍😍,0,sports
সাবাস বেটা,0,sports
অনেক কষ্ট লাগতেছে!!,0,sports
আফগানিস্তান ইতিহাস করবে বাংলাদেশ ওদের কাছথেকে টেস্ট সিকা দরকার,0,sports
কথাগুলো যৌক্তিক কারন সংবাদ সম্মেলনের আগে বসিবি কে ইনফরম করা দরকার ছিলনা করেই আন্দোলন টিক হয়নিযাই হোক এই সমস্যার দ্রুত সমাধান হোক বাংলাদেশ ক্রিকেটের কল্যানেই।।,0,sports
"বিষয় হলো: বাংলাদেশ হোইট ওয়াশ হইছে,,সো গন্ধ যেন মাশরাফির গায়ে না যায়,,তাই মাশরাফি নিজে বাচতে গিয়ে সাব্বিরকে ইশারা করে ঘোলা পানিতে মাছ শিকার করেছে,করাণ সে এখন রাজনীতিবীদ",0,sports
লিখিত বক্তব্য দেওয়ার জন্য বাদ্য করা হচ্ছে।,0,sports
রুবেল দোস্ত তুই জিনিয়াস অসাম দোস্ত তুই comedian actor হওয়া দরকার ছিল ।রুবেল দোস্ত তুই সত্যি নির্ভীক ও সাহসী বটে । এই দোস্ত এগিয়ে যাও তোমার সাথে পেইজ বল ভাইঙ্গা দিমু রাখবা কোন সমস্যা নাই ।,0,sports
ফিনিশ হয়ে যাবে ফিনিশ🤣🤣,0,sports
কুটি টাকা বছরে কি করো তোমরা চুরের মার বড় গলা,0,sports
প্রথমত কোনো যুক্তি নাই লজিক নাই। যক্তি তুমার কাছে মনে হলেও এর কোনো প্রমান নাই। ধর্ম কে কারা পুজি করে তার প্রমান দিলে শেষ হবেনা। মনে হলো পাচ বছরের বাচ্ছা একটা ক্যামেরা পেয়ে যা ভাল লাগছে একা একা বকে গেল। রাবিশ নাহিদ,0,sports
যে দর্শকদের জন্য নাম ডাক তাদেরকে হুমকি অহংকার পতনের মূল,0,sports
ভাইয়ের ফ্যানরা কই হাত তোলেন??🖖🖖🖖🖖,0,sports
অবশ্যই চাইবে ঠিক আছে সাকিবুল আসলাম না থাকলে বাংলাদেশের ক্রিকেট ধ্বংস হয়ে যাবে ঠিক আছে কিন্তু পাপন পাপন এর তো আর কি বলবা পরিষ্কার করে না কেন এখনো বছর আগের কথা এখন রাজনীতির জন্য এটাতো পাপড়ি,0,sports
কে কে সুজনের জন্য খুলনা নেন নাই,0,sports
বাংলাদেশ ক্রিকেট নিপাত যাক যেখানে সাকিব নেই সেখানে এই ক্রিকেটকেই বিদায় দিলাম।,0,sports
ওওওওওওওসেই মুশফিক ভাই,0,sports
ধন্যবাদ কুমিল্লা,0,sports
যদি ভুল খবর হয় তবে আপনি ক্ষমা চেয়েনাও। এহকালে ক্ষমা হবে পরকালে খারাপ হবে,0,sports
সাকিব কে আবার দলে দেখতে চাইসবাই কী একমত,0,sports
আমি আর খেলা দেখবো না কেনো সাকিব আল হাসান নেই তাই পাপন কে জুতা মারো সবাই,0,sports
সত্যি বলছি সাকিব ভাইকে দেখে চোখের পানি ধরে রাখতে পারিনি।ভাই আপনার জন্য আমাদের ভালবাসা আর সম্মান কখনও কমবে না বরং বারবে।❤,0,sports
"হুদাই,, খায়া দায়া কোনো কাজ নাই?????",0,sports
পাপন তার বাপের নাম ডিবিয়ে দিয়েছে আমাদের বাংলাদেশ আর আগাবে না,0,sports
লিটন দাস ব্যাটিং ভাল করুক আর নাই করুক আমার কাছে তার ব্যাটিং স্টাইল জোস লাগে।,0,sports
খেলা চুদার টাইম নেই,0,sports
আমিও আর খেলা দেখব না,0,sports
ভাই নিবার পরই লাল সালাম দেই এইটা দেখার মত কিন্তু এর একটা খেলোয়াড় এইটা আগে করে। আর একটা অনুরোধ আমি ফানি ভিডিও বানাই বেশি ভালো হয় না তবুও আপনাদেরকে দাওয়াত রইলো,0,sports
উস্তাদ তোমি না খেললে আর জিবনে খেলাই দেখবনা বলেদিলাম,0,sports
সাকিব ক্রিকেট খেলা শিখছো কিন্ত রাজনিতি শিখনাই তুমি রাজনিতির ফান্দে পড়ছো এখান থেকে বাদ বাকি ক্রিকেটারদের শিক্ষা নেয়া উচিৎ।,0,sports
সাকিবের অভাবে সারা জীবন ভুগবে বাংলাদেশ।,0,sports
আই লাভ ইউ মুশফিক♥♥♥,0,sports
পাপনকে বাদ দিয়া হক,0,sports
আমি কি বলবো?আমার আগের বক্তারা সকলেই বলে গেছেন আমার পরে যারা আসবেন তারাও বলবেন।তবে পাপনের পদত্যাগ চাই এটাই বলতে পারি।এই যায়গায় কমেন্ট পরছে পাপনের বিরুদ্ধে।যমুনা টিভির সাংবাদিক ভাই আপনারা এই নিউজটা করে দিয়েন আপনার পদত্যাগ চায় দেশের ক্রিকেট প্রেমী সবাই।,0,sports
তবুও জাতীয় দলে আসবে না।কোন লাভ নাই,0,sports
কি বলবো বাংলাদেশ এটা সাবাবিক,0,sports
ওনার সব আপডেট জানার চেষ্টা করবেন!! আর যতটুকু সম্ভব আমাদের জানাবেন।,0,sports
শুভকামনা মাশরাফি ভাই 😎😎😍😍,0,sports
বাংলাদেশের ফুটবল টাকে যেমন নষ্ট করা হয়েছে ঠিক তেমনি ভাবে ক্রিকেট টাকে নষ্ঠ করা হচ্ছে !! কি হবে এদেশেরকোথায় আছি আমরা।,0,sports
সব সরযন্ত কে নষ্ট করার জন্য!!!,0,sports
এবার খুলনা কাপ নিবে। একমত হলে লাইক দিন।,0,sports
আফিফ কে নিয়ে মাতামাতি বারাবারি ছাড়া আর কিছুই না ও কোন খেলোয়াড় না আর নাইম শুরুর মোমেন্টাম ধরে রাখতে পারেনা থেকে ওভারের পর ওর সিংগেল নিতেই কষ্ট হয়,0,sports
খেলা হবে খেলালালা হবেবে 😀,0,sports
কেসিনো পাপন,0,sports
কে হারবে কে জিতবে এটা মাঠে নামার আগেই জেনে যায়। তুই পাপন এটা বল কিসের জন্য । রাজনীতি চোদাও খেলার মাঠে,0,sports
সাকিব বাংলাদেশের হয়ে খেলবে ফালতু মি প্লান অ্যাপ কেন ভাই এসব দেখে কি এখনো বিশ্বাস করেন প্লিজ বিশ্বাস করবেন না বাংলাদেশের হয়ে সাকিব খেলবে এটা গ্যারান্টি,0,sports
সবাই কি মাস্তান হয়ে গেছে দেখলাম না বেটা তগ খেলা আফগানিস্থানের কাছে হারে লজ্জা করে না,0,sports
"যাক আপনার আপনার কথাগুলি ভালো লেগেছে। সব আল্ট্রা লিগেন্ড সাংবাদিক থেকে আলাদা। যেমন বেদ চুদুরীর পিছনে আগুন লেগে গিয়েছিল সাব্বির দলে আসার পর, আশা করি আগুনের উত্তাপটা গতকালের পর সাব্বির আরো বাড়াইয়া দিছে 😁😁😂😂",0,sports
মুশফিকের জন্য বুকের বাম পাশে যেন ব্যাথা করছে💔,0,sports
বাংলাদেশ টিম এ দ্বিতীয় মুশফিক আর হবেনা । আমি মনে করি মুশফিক ভাই একজন ভালো মনের মানুষ ।,0,sports
ঢাকালিগে আমপাইয়ার দুরনিতি বন্ধ এটা পাপনের ভূয়া কথাএবং কেমেরা সবগুলো খেলাতে লাগানো হইসে এটাও পাপনের ভূয়া কথাভবিষ্যৎ এর উন্নিরত জন্য এই জাগাটাই নজরদারি বারাতে হবে এবং দূরনিতি মূক্ত রাখতে হবে ।,0,sports
মুশফিক ❤❤❤❤,0,sports
ছাব্বির কাকু আসলেই একটা অরিজিনাল বেয়াদব ওকে তো কম হলে ও ১০ বৎসর নিশিদ্ধ করা উচিৎ ছিল সালা বেয়াদব,0,sports
কে যদি নিষিদ্ধ করা হয় তাহলে বাংলাদেশের মানুষ কখনো বিচিবি কে ক্ষমা করা হবেনা। কে কে একমত?,0,sports
বদমাইশ,0,sports
আচ্ছা আমি বুঝলাম না বছর পর চেক করলো কেন।আগে কি করছে। নাকি ফাদে ফালানোর জন্য ওর দোশ খুজে বের করছে।,0,sports
ভাল হবে,0,sports
এটা ফাউল কথা,0,sports
চামচা গোলি দের পিটানুর দরকার চামচারা খেলা কি বোজে,0,sports
দুঃখিত আমি তাসকিনকে খুব ভাল বলার বলব না যদিও সে চারটি উইকেট পাইছে কিন্তু এখানে ভালো বলা হয়েছে মাত্র শোয়েব মালিকের শোয়েব মালিককে যে বল দিয়ে আউট করছে সেই ভুলটা ছিল ভাল বাকিগুলা বেসমেন্ট ভালো ভালো শট খেলতে পারে নাই সেজন্য আউট হয়েছে তাসকিন লাইন লেন্থ ভালভাবে বল,0,sports
মুশফিক পাগল হইয়া গেচে 🙉🙉🙉,0,sports
নাসিরের জাতীয় দলের ক্যারিয়ার শেষ। ঘরোয়া লীগও হুমকীর মুখে। পার্সোনাল লাইফে শৃঙ্খলা না থাকলে তার প্রভাব অবশ্যই খেলায় পড়বেই। পাপন এই সুযোগেরই অপেক্ষায় ছিল। দেশের ক্রিকেটের এক আক্ষেপের নাম হয়ে থাকবে নাসির হোসেন। আর সাব্বিরের জন্যও এটি একটি সতর্কবার্তা।,0,sports
পাপনন পাপ🤪পাপ হটাও বাংলাদেশ ক্রিকেট বাচাও।,0,sports
কোন কিছুই হত না যদি আন্দোলন না করতো এখন অনেক কিছুই হবে। একটা ফোন কল অনুসন্ধান করার জন্য আইসিসির দুই বছর সময় লাগলো!! আর তার ফলাফল দেয়ার সময় হল এই আন্দোলন করার পর!! বাহ কি সুন্দর মিল!!,0,sports
কতি হবে,0,sports
অসাধারণ একটি ব্যাটিং করলেন,0,sports
তাজকিন এর মাথা ঠিক নাই,0,sports
বাল লাগলেনা কুমিল্লা হাইড়া গেছে,0,sports
কথা গুলো সহজ করে বল্লে কি হয় রিপোটার ভাই। সাকিব আমাদের গর্ব। সাকিব কোন দোস করে নাই তাই ভালো ভাবে বলা যায়,0,sports
ইন্ডিয়ার দালাল জুতা মারি ওদের কপালে,0,sports
দুই বছর আগের ঘটনা আইসিসির কাছে এখন কিবাবে জায়,0,sports
শাকিবকে বাদ দিয়ে ভারতের বিপক্ষে সুন্দর ভাবে হারার জন্য শাকিবের সাথে এতো কিছু,0,sports
হাইলাইটসের খবর নাই আছেন উইনিং মোমেন্ট নিয়ে উইনিং মোমেন্টর জন্য সংবাদ চ্যানেল আছে,0,sports
পাপুন্দা তো পা পুন্দা,0,sports
সবাই আপন হয়না রেকেউ কেউ পাপন ও হয়🙄,0,sports
বন্ধু অস্থির মাল খাইছো,0,sports
ওর বাপের টাকা দেয়,0,sports
বেদব তো বেদবী,0,sports
ভালো হতে টাকা লাগে না,0,sports
পাপন বাংলাদেশ ক্রিকেটকে ধ্বংস করে দাফন করে ছাড়বে সবাই মিলে পাপনরুগ তাড়াতে হবে,0,sports
বছর কৃকেটারদের বেশ টাকা পাইছেতো সেজন্য খুব তেল দারায়ছে এতদিন মাশরাফি ছিল তখন কিছু হয়নি মাশরাফি যাওয়া মাএই সাকিবের ফাজলামি শুরু হয়েগেছে আপনি ঠিকই বলেছেন পাপন সরে গিয়ে আপনারে ওই চেয়ারে বসালে ভাল হতো তাইনা,0,sports
গালি দিয়েতু কি হইছে,0,sports
সকলের বেতন। টাকা করা হউক।,0,sports
"পিরীতের আঠা রে,<br /> টান দিলে ছুডে না!",0,sports
তে ইন্ডিয়া তে ক্রিকেট সেন্টার,0,sports
গালি দিছে ত কি হয়েছে।,0,sports
পাপন অভিযোগ করেছে আসিসির কাছেতাছাড়া এত দিন এই ব্যাপারে জানতো না এখন কিভাবে জানলো।আন্দোলনের কারনে সাকিবের উপর পাপনের রাগ এই রাগ থেকে পাপন এই গুটিবাজি করেছে।পাপনের পদত্যাগ চাই,0,sports
পাপোন চোর,0,sports
তীব্র নিন্দা জানাচ্ছি,0,sports
বাহ বাহ,0,sports
বুকাসুকা,0,sports
অনেক বড় ফাজিল ....................,0,sports
আমারে কেও মাইরা লাও 😂😂😂🤣🤣🤣🤣😅😅😅,0,sports
সাকিব আল হাসানের মতো একি রকম বোলিং ব্যাটিং দেখুন আমার চ্যানেলে শেখ সাকিব আল হাসান একদম একি রকম বোলিং ব্যাটিং করে,0,sports
পাপন খুব খুসি,0,sports
নুরুল হাসান সোয়ান অপে দিয়ে একটা বা মারতে পারলে বার কানে ধরে উঠ বস করমু লেগ ছাড়া কোন দিকে খেলতে পারে না 🍌🍌🍌🍌,0,sports
বাংলাদেশ ক্রিকেট টিম টাই ধংস হয়ে গেল।দোষী যারা তারা ক্ষমা চাইবে।সাকিব ভাই কেন চাইলে ন,0,sports
এটা সত্যি মনে হচ্ছে না,0,sports
যার যেখানে খমতা সে সে ভাবে দেখায়।জেমন পাপন।,0,sports
আগে বাগে সব কিছু দিয়ে দিলে এমন হওয়া টাই স্বাভাবিক খারাপ মেয়ে,0,sports
সাকিবের সাথে বাংলাদেশের প্রধান বিচারপতি এস কে সিনহার মতো গেম খেলা হয়েচে,0,sports
সব কিছুর একটা কারণ আছে কিন্তু কারণ কি সেটা তো বললেন না ।,0,sports
সাকিব ভাই পাপন সাহেবকে একটু বলে দেও যাতে সৌম্যকে যেন টেস্ট স্কোয়াডে অন্তর্ভুক্ত করে।,0,sports
যারাযারা পাপনের সম্পদ হিসেব চান তারা লাইক দিয়ে যান 👉👉👍যমুনা টেলিভিশনের ইনভেস্টিগেটরদের অনুরোধ জানাচ্ছি,0,sports
আজ মনটা অনেক খারাপ ছিল কিন্তু তোমগো কমেন্ট পরে আবার মনটা ভালো হয়ে গেল,0,sports
ওয়াহাব রিয়াজ ভাই স্টার।,0,sports
"রুবেলের এই প্রতারণার কারণেই<br />আজ হেপির জীবন বদলে গেছে <br />সে এখন একজন পরহেজগার <br />মহিলায় পরিণত হয়েছে,, আসুন<br />আমরা সবাই হেপির মতো ইসলামের <br />আলোর পথ অনুসরণ করি পাচ ওয়াক্ত <br />নামাজ আদায় করি। 👍👍👍👍👍",0,sports
ভাই অনেক কান্না করছি কথাটা সোনার পর,0,sports
ইসলাম ধর্ম এত দুর্বল ধর্ম না যে দুনিয়ার মিথ্যা কথা চাপাবাজি গাঁজাখুরি গল্প ফেঁদে আমাদের এই পবিত্র ধর্মের প্রচার করতে হবে। এসব ভণ্ডদের কারনে ইসলাম ধর্মকে মানুষ হালকা করে দেখার সুযোগ পায়। পবিত্র ধর্ম ইসলামের জন্য আজ এই ভিডিও বানাতে বাধ্য হলাম। তা না হলে আমার পবিত্র ধর্মকে এরা ধংস করে দিবে। তু চিজ বাড়ি হ্যাঁ মাস্ত মাস্ত এরকম অশ্লীল গানের সুর নকল করে আল্লাহ এবং পবিত্র কোরানের বানী প্রচার করছে ?? এদের সাহস কত বড় আমার ধর্মকে অপমান করে !!!,0,sports
ফারুকের যায়গায় অামাকে লাগতো,0,sports
ভালো লাগে যখন বিগ স্কোরিং ম্যাচ হয় ❤,0,sports
এক হাতে তালি বাজে না।,0,sports
"বাঙালী সারাটাজীবন বেশী পাকনামি করে গেলো,,খুজে দেখেন,,প্রত্যেকটা মানুষের এই কিছুনা কিছু দোষ আছে,,অন্যান্য দেশে প্লেয়াররা কোন ভূল করলে সেটার বিচার হয়না,,কারন তারা দেশের একটা সম্পদ কে নষ্ট করতে চায়না,,আর আমাদের দেশেই যতো সব মাদবরি,,অন্যান্য দেশে প্লেয়াররা ভুল করলেও সেটা ঢেকে রাখে সে দেশের জনগন মিডিয়া সবাই,,আর আমাদের দেশে কি হয়,,মাঝে মাঝে লজ্জা হয় এটা ভেবে কেনো বাঙালী হলাম",0,sports
বড় বড় কথা বলেচোরের বাবার বড় গলা৷,0,sports
ভাই পাপন ঠিক করেনি সাকিবের পাসে আমরা সবাই আছি?????,0,sports
পাপনের পদত্যাগ চাই ☺,0,sports
কোন সমস্যা নাই বস আমরা তোমার সাথে আছি তোমার জন্য হৃদয়ের মণিকোঠায় অনেক অনেক ভালোবাসা জমা আছে সমালোচকরা সমালোচনা করবেই কারণ তাদের কাজ এটাই শুভকামনা রইল বস এগিয়ে যাও,0,sports
সালাসিটিন,0,sports
এ কথা শুনে আমরা অনেক হ্যাপি হলাম!,0,sports
ভাই আবার ফিরে চাই শাকিব হাসান ক,0,sports
বাংলাদেশের গণমাধ্যম মিথ্যেবাদী শুধু মিথ্যে ছড়াচ্ছে আফগানিস্তান বাংলাদেশকে হারায় নি আসল কারণ হচ্ছে ভারত চোর চোর চোর বাংলাদেশ তো টাইগার যারা বিশ বছর ধরে টেস্ট খেলছে টি টেস্টের পর জয় লাভ করেছে এমন এক শ্রেষ্ঠ দল তারা আবার কি করে হারতে পারে? সব চক্রান্ত,0,sports
এরকম হাজার ও সাকিব ধ্বংস করা সহজ কিন্তুু এরকম একটা সাকিব তৈরি করা খুব কঠিন???,0,sports
তাসকিন আমার প্রিয় খেলোয়ার,0,sports
কথা একটাই এই আবাল পাপন রে ক্রিকেট থেকে আগে সরাতে হবেকারন এই খবর ও কোথায় থেকে শুনেছে সেটা বের করলেই সে ধরা,0,sports
"সাব্বির বেড বয় না,গুড বয় ওকে নিন্দকের দল",0,sports
অসাধারন জুটি মুশি আর মিরাজ,0,sports
ডানে গরু বামে খাসি ইম্রুল ব্রো কে আমরা ভালবাসি 🥰🥰🥰🥰,0,sports
পাপনের পদত্যাগ যারা চান লাইক দিন আর যারা চান না কমেন্টের রিপ্লাই দিন।,0,sports
নাহিদরেইন আপদ মস্তক একজন ভন্ড যিনি কিনা আওয়ামীলিগের একজন সক্রিয় এজন্ট যার কাজ হল সোসাল মিডিয়াতে সরকারের বিরুদ্ধ্যে সাধারণ ছাত্রদের যত যুক্তিক আন্দোলন ছিল বা আছে সব আন্দোলন গুলো কে তিনি নেগেটিভ ভাবে জাতীর সামনে নিয়মিত চাপা বাজি করতেন এবং করেন নিচে বিস্তারিত আলোচনা করা হলঃ তিনি কোটা বিরধী আন্দোলন নিরপেক্ষ ভাবে বিশ্লেষণ না করে ভুল ভাবে এক পেশে কোটা বিরধীদের নেগেটিভ ভাবে উপস্থাপনা করে পক্ষান্তরে চাম চামি দালালী করেছেন ? নিরাপদ সরক আন্দোলনের যুক্তিক দাবিকে ভ্রান্ত বলে ছাত্রদের ব্যাপারে উল্টা পাল্টা মন্তব্য করে পক্ষান্তরে আওয়ামীলীগের চাম চামি ও দালালী করেছেন ? ভিপী নুরু কে কোন রুপ প্রমান ছাড়া দুর্নীতি বাজ ও চাদা বাজ আক্ষাদিয়ে তার বিরুদ্ধ্যে উল্টা পাল্টা ভিডিও বানিয়েছেন !! নির্বাচন কে নিরপেক্ষ ভাবে বিশ্লেষণ না করে একটি দলের পক্ষ্যে ভোট চেয়ে সেই দল আওয়ামীলিগ এর দালালী করেছেন ! এই থেকে কি প্রমানিত হয় না যে আপনে একজন দালাল !! আলোচন করলে নিজেকে নিরপেক্ষ রেখে দুই পক্ষ নিয়েই সমান ভাবে আলোচনা করেন দালালি আর ফাইদা সুবিধার জন্যে ভন্ডামি ছাড়েন !! তার ভন্ডামির নমুনা দেখেনঃ তাকে কোন দিন ভোট চুরি ডাকাতি নিয়ে ভিডিও বানাতে দেখবেন না ? তাকে কখন ছাত্রলীগের টেন্ডার বাজি চাদা বাজি বিরুধ্যে কখন ভিডিও বানাতে দেখবেন না ? পুলিশের দুর্নীতি ও মাদক চোরা চালান নিয়ে ভিডিও বানাতে দেখবেন না ? কেসিনো কেলেংকারি তাকে ভিডিও বানাতে দেখবেন না ? আবরার হত্য নিয়ে ভিডিও বানাতে দেখবেন না ? নাহিদের কাছে এই প্রেশ্ন গুলো রেখে গেলাম আশা করি উত্তর দিবে সে ? শেষে একটা কথা বলতে চাই ভন্ডামি বাদ দাও !! তোমার নিজের পাছাতেই অনেক গু আগে নিজের গু ছাফ করো তার পর অন্য জনের পাছায় হাত দিয়ও,0,sports
ভাইয়া পাপনের ক্যাসিনো ভিডিও নিয়ে রিপোট করবেন,0,sports
কাজ টা খুব খারাপ হলে 👎👎👎👎👎👎👎👎👎👎👎👎👎👎👎👎👎👎👎👎👎👎👎👎👎👎👎👎👎👎👎👎👎,0,sports
বাংলাদেশ ক্রিকেট কে ধ্বংস করার ষড়যন্ত্র চলতেছে,0,sports
সব দোষ পাপনের সাকিব না থাকলে বাংলাদেশের কেলা ধ্বংস হয়ে যাবে এটা পাপনের একটা চাল পাপনের পদত্যাগ চাই আমরা,0,sports
তাছিন ভাইয়া মিরাজ কেন ইন্ডিয়া সফরে নাই? পাপন্দা কি ওকেও ব্যান করে দিছে?? উত্তর চাই ভাইয়া,0,sports
আমাদের সাকিব ভাই কে আমার আবার চাই,0,sports
সাব্বির কে জুতা মারতে ইচ্ছে করে👠👡👠👡,0,sports
কারও না কারও হাত তো অবশ্যই আছে হায়রে দেশের মানুষ বড় বড় মানুষের হিংসা,0,sports
ভারতের দালাল,0,sports
আগে নিজের টা বাবেন,0,sports
সত্য কথা ভাই,0,sports
ধারাবাহিকতা দরকার,0,sports
সিলেটিদের জাতীয় খাদ্য পান শুনেছি মাচে ভাতে বাংগালী ওরা পানে সুপারি বাংগালী। 😁😁😁😎,0,sports
এই শালাক এই ভাবে মারা লাগবে,0,sports
সাকিব কে ধংস করা মানে বাংলাদেশ ক্রিকেট ধংসটিক ই বলেছেন টিপু ভাই,0,sports
প্রধানমন্ত্রীর আশকারা পেয়েই পাপন ধরাকে সরা জ্ঞান করছেনপ্রধানমন্ত্রী কি জানেন পাপন টি ক্লাবকে পয়েন্ট করে দিয়ে ক্ষমতা কুক্ষিগতো করেছেন? প্রধানমন্ত্রী কি জানেন দূর্জয় একসাথে বিসিবি পরিচালক এবং কোয়াব সভাপতি? কোয়াব সম্পাদক দেবব্রত একইসাথে বিসিবি রেফারী হিসেবে টাকা বেতন নেনবিসিবির সব পরিচালক দুর্নীতিবাজসুজন একসাথে একাধিক দায়িত্ব পালন করেন বেতন নেন অনেকক্যাসিনোতে টাকা উড়ান! বিসিবির মল্লিক বিপিএলের মাধ্যমে অনেক টাকা বাগিয়ে নেনকিন্তু খেলোয়াররা নায্য টাকা পান না। অথচ পাইলটশান্তবুলবুলরা অবহেলিত “জাতীয় লীগের ম্যাচের আগেই জানা যায় কে জিতবে? “সাকিব। আর্থিক দাবির আড়ালে খেলোয়াররা এসব দুর্নীতির বিরুদ্ধে ধর্মঘট করছেনবিসিবিতে শুদ্ধি অভিযান এখন জরুরী,0,sports
অনেকগুলো বিষয় বাদ গেছে ভাই।শুধু সাকিনকে নিয়ে বললেন।বর্তমানের ক্রিকেট আর ক্রিকেট বোর্ডের কমকর্তাদের অনেক কান্ড বাদ গেছে।,0,sports
বর খেলোয়ার হয়েছে দেখে কোন কথা বলা জাবে না মুশফিক পাগল হয়ে গেছে,0,sports
প্রতিটি খেলোয়াড় কে অনুরোধ করবো আন্দোলন শুধু শাকিবের স্বার্থের জন্য ছিল না প্রতিটি খেলোয়াড়ের এই স্বার্থের জন্য ছিল সাংবাদিক সম্মেলনে পাপনের কথায় বোঝা যায় যে এই নিষেধাজ্ঞা আইসিসি নয় বিসিবির তাই সবাইকে ভারত সফর বয়কট করতে হবে,0,sports
সাকিবের কিছু হলে পাপন এর বিরুদ্ধ্বে ঝড় হবে পুরো বাংলাদেশে ইনশা আল্লাহ,0,sports
সাবাস সাব্বির,0,sports
খুশি হয়েছি,0,sports
যারা ইউটিউবফেসবুক ব্যবহার করে তারা এই সব বিষয়ে জ্ঞান রাখে। এই ভিডিও যারা দেখেছে তাদের মধ্য একজনকেও পাওয়া যাবে না যে এ বিষয়ে জানে না। মোটামুটি সবাই জানে। পাপোন্দার দিন শেষ। এই সব ভিডিও আরো আগে বানাতে হয়। বেশি পুরনো হয়ে গেছে। পারলে ইসকন নিয়ে একটা ভিডিও বানান।,0,sports
পাপন কে অাগে বাদ চাই,0,sports
সালের বিপিএলটা হলো রাজনৈতিক নেতাদের বিপিএল এটা গনতান্ত্রিক বিপিএল নয় যে এখান থেকে জনগণ বা মালিক পক্ষ লাভবান কথা বলার অনধিকার রাখেনা আমি মনে করি।,0,sports
লোভি সাকিব।।। পাপন,0,sports
পাপন সাহেব শুধু আন্তজার্তিক খেলা নিয়ে ই বললেন কিন্তু ওনি আসার পর কতগুলো ঘরোয়া লিগের খেলা বন্ধ করেছেন এটা সবাই জানে। ম্যাচ পাতানো থেকে শুরু করে কি হয় না দেশের ঘড়োয়া খেলাগুলোতে। এই ব্যাপারে তো কিছুই বললেন না। !,0,sports
রাসেল ইনশাল্লাহ বলে নি মনে হয় পুরো পৃথিবী জয় করে পেলেছে ৷,0,sports
এমন ভাবে ধরে নিয়া যাইতাছে মনে হয় ক্রস ফায়ারিং করবো হায়রে মানুষ এর ব্যবহার এর ন্যূনতম ভদ্রতা আজ হারিয়ে গেছে।।,0,sports
বিসিবি কে না জানিয়ে শুধু শুধু আন্দোলন করার কি প্রয়োজন ছিল গাধার বাচ্চারা বিসিবিকে জানাবি আগে,0,sports
বিশ বছরে আমরা কেন ভালো মানের খেলোয়াড় তৈরি করতে পারি নাই এই ব্যার্থতা কাদের? ভালো পেস বোলার স্পিনার নেই ?ঘরোয়া কাঠামো ঠিক করেন তৃণমূল পর্যায়ে থেকে খেলোয়াড় উঠে এনে পরিচর্যা করেন পাইপলাইন শক্তিশালী তৈরি করেন যেন খেলোয়াড়দের মধ্যে প্রতিযোগীতা তৈরি হয় এইভাবে চললে বাংলাদেশ ক্রিকেট ধ্বংস হতে সময় লাগবে না ।,0,sports
ধন্যবাদ,0,sports
তাকে এখন আর কোনো দরকার নেই,0,sports
মুশফিকুর রহিম অনেক অনেক অভিনন্দন যারা মুশফিকের ফ্যানরা লাইক দিন,0,sports
খানকির পোলারা,0,sports
যে দল মোসাদ্দেক এর মতো খেলোয়ারকে অধিনায়ক করে দল গঠন করে তাদের থেকে এর বেশি আর কি আশা করা যায়।।।এবারের বিপিএল এর থার্ডক্লাস দল সিলেট থান্ডার।,0,sports
তোমার পাপন বাবা যে সব ফাঁস করছেতার কথা কে বলবেপাপন এর মূল কারিগর,0,sports
সাকিব ইংলেন্ডে খেলুক আমারা সবাই চাই কি বলেন আপনারা!!!,0,sports
আচ্ছা সাব্বিরের permission ব্যাতিত আপনারা কিভাবে তার ফোন নম্বর স্কৃনে দেখালেন এটা কি অপরাধ না??!!,0,sports
শাকিব বাংলাদেশে খেরলে ভালো হবে,0,sports
ভারতের দালাল তুই শালা,0,sports
মেয়েদের যে পছন্দ দেশে কি আর ছেলে নাই কাটাস নি কাটাসের সাথে প্রেম করে,0,sports
শান্তর থেকে সাইফ হাসান ভালো,0,sports
সামনের সিরিজে ভারতের সাফট করব ইনশাল্লাহ,0,sports
সাববিরকে দল থেকে বাদ দেয়া হোক এবং আজীবন নিষিদধ করা হোক,0,sports
আইসিসির সাথে পাপনের গোপন ফোনআলাপ অচিরেই বের হবে।,0,sports
খুলনা আজ লাষ্ট তিন ওভারে যে রান দিয়েছে সে রান গুলো খুলনার জন্য কাল হয়ে এসেছে,0,sports
ভাই সাকিব আবার ফিরবে ♥,0,sports
বাংলাদেশ থেকে ক্রিকেট খেলা নিষিদ্ধ করে দিয়ে অস্ট্রেলিয়ান গাভী পালন করলে বেশি লাভবান হওয়া যাবেদেশ এগিয়ে যাবেহতাশা কাপছাড়া এপর্যন্ত কোন কাপ অানতে পারে নাই তাহলে কি লাভ এই ক্রিকেট দল দিয়েসুতরাং বেতন বাড়ানোর জন্য অান্দোলন করা তো লজ্জাহীনতার পরিচয়।,0,sports
যি আমরা অনেক জন মিলে দেখছি আমরা সবাই চাই সে আবার ক্রিকেটে ফিরে যাক?,0,sports
রিয়াদ ভাইয়ের ভাগ্য খারাপ,0,sports
তাসকিন আর ফিজ এর জন্য খারপ লাগছে,0,sports
খুলনার সবাই অনেক ধারারবাহিক খেলছে। খুলনা শিরোপা জিতবে,0,sports
পাপনের এ জুতা দিয়ে বাইরানি দরকার,0,sports
ভাই আপনি তো অনেক সুন্দর কথা বলেছেন,0,sports
বাংলাদেশের ক্রিকেট কে বাঁচাতে হলে পাপন কে সরাতে হবে। বেশি কথা না বলে পদত্যাগ করেন।,0,sports
অসাধারণ একটি এপিসোড ছিল👌যে দেশে গুণীজনের সম্মান নাইসে দেশে গুনী জন্মায়না।তাইতো আমরাও গুণীজনের কদর করতে জানিনি।পাপন তার নিজের স্থানটি পাকাপোক্ত করতে যা যা করনীয় ঠিক তাই করেছেএতে সাকিব কেন পুরো ক্রিকেট ধ্বংস হলেও তার কিচ্ছু যায় আসেনা।শেষটা খুবই হৃদয়বিদারক ছিল যখন প্রিয় মুখ সাকিবকে দেখলামসাথে ছিল হৃদয়স্পর্শী একটি ব্যাকগ্রাউন্ড সাউন্ড।ফিরে এসো সাকিব আরো তীক্ষ্ণভাবে! ✌,0,sports
শালা জুয়ারি দুর্নিতী বাজ দিনের জন্য এসে এখানে ঘাপটি মেরে বসে আছে মনে হয় বিসিবি তার পৈত্রিক সম্পত্তিলাথি মেরে বিদায় করো এদের,0,sports
পাগল মেয়ে,0,sports
ওদের থেকে জাতি অনেক শিক্ষা নিতে পারে।,0,sports
"আমরা বাঙালিরা কত বড় খারাপ হইতে পারি,, যখন শুভা খারাপ ভাষায় কথা বলে তখন অই মেয়েকে সবাই খারাপ বলে।। আর রুবেল যখন খারাপ কথা বলে তখনও হ্যাপিকেও খারাপ বলে",0,sports
রাসেল কি মানুষ নাকি রে।এলিয়েন মনেয়,0,sports
সৌম্য সরকার যদি এইভাবে জাতীয় দলে ভাল খেলতে পারে তাহলে বাংলাদেশ দল আরও শক্তিশালি দলে হিসাবে সাহায্য করবে।,0,sports
সাব্বাস চট্টগ্রাম এগিয়ে যাও,0,sports
আপনার চরিত্র ঠিক করেন আগে সালারা আর কোন খবর পাওনা,0,sports
সিজদা দেয়া টা চোখে পড়লো না????<br />সত্যি কিছু সাংবাদিকদের প্রশ্ন গুলি খুব ডিসাপোয়েন্টিং 😔,0,sports
"পাপের পরিমাণ বেড়ে গেছে,,শাস্তি পাবেই",0,sports
মাহমুদউল্লাহ ভাইয়ের বাউন্ডারি হাঁকান গুলা সেই হইছে।,0,sports
একজন পাপন! আইসিস কি কোন কথা বলছে এখন শুধু সাকিব কে জড়িয়ে এখন নিজের গোমড় ঢাকছেন।।,0,sports
ধন্যবাদ ভাই আপনি ভালো বলেছেন।,0,sports
ভালো ব্যাটিং করবে কেমনে??? এইসব করেই সময় পায় না।,0,sports
এটা কি রে ভাই। মানুষরে বোকা পাইছছ। কোথাকার ভিডিও কোথায় নিয়ে এডিট করছছ।,0,sports
গান কোই😠😠😠,0,sports
গানটার জন্য শুভকামনা এবং ভালোবাসা রইলো কিন্তু গান ওইটাই সবচেয়ে মানে সাবাস বাংলাদেশ সবার মনে একটাই হৃদয়ে জায়গা করে নিয়েছে,0,sports
বিপিএলে আপনাকে স্বাগতম গেইল ভাইয়া।,0,sports
পাপোন্দা এর কিছু জারজ সন্তান আছে তারা আনলাইক দিয়েছে 😡😡😡,0,sports
পাপন এর পদত্যাগ চায়।,0,sports
পদতেক চাই পাপনের,0,sports
ভাই সাকিব এর ভুল সামান্য না। বুকিদের কথা কাউকে না বলা কিন্তু এক রকমের তাদের সাপোর্ট করা আর ভুল একবার মানা যায় তিনবার না!,0,sports
মেয়েরা বসায় যায় ছেলেরা নয়। এরা মোবাঃ মাগি।তাদের বিচার হোক।এরা এসে ছেলে দের বিপদে ফালায়।,0,sports
বদনাম বার করার কাজ ই তা আমাদের সামবাদিক ভাই দের।।।,0,sports
সাকিব যদি নিষিদ্ধ হয়তাহলে আমি ব্যক্তিগতভাবে আন্দোলনে নামবো,0,sports
ভালোবাসা অবিরাম সাকিবের জন্য 😍😍😍,0,sports
ভাই তাহমিদ অমিত। টক শো বানান আপনার এই চ্যানেলে।,0,sports
বেরি নাইচ বলার মেদি হাছানরানা,0,sports
ভাই অন্ধ লোকেরা কি দেখলোনা <br />সাব্বির .100 করার পর <br />প্রথমে তার আঙ্গুল দিয়ে বেটকে ইশারা করে তার পর সে তার উজ্জাপন করলো <br />ভালো মানুষ ভালো চৌকে দেখে <br />খারাফ লোক কারাফ বাবে এটাই মানুষের স্বভাব,0,sports
"সাব্বির যতদিন আছে,আমি বাংলাদেশ এর কোনও মাচ দেখব না",0,sports
আমি পাপন এর সাথে সংবাদ এ যদি সরাসরি কথা বলতে পাতাম তাহলে একটা কথা জিজ্ঞাসা করতাম যে যখনি তাকে কিছু জিজ্ঞাসা করা হয় তখনি উনি বলে আমি এই বিষয় কিছু জানি নাউনি যদি না জানে তাহলে যানেটা কে??? আর প্রতি বার খেলয়ার নির্বাচনে ভুল হয় প্ল্যান এ ভুল হয় তাহলে বার বার আবার তাদের কেই কেনো দায়িত্ব দেয়া হয়??আর এদের বিকল্প যদি কেউ না থাকে তাহলে এর জন্ন্য দায়ি??? আপনি এতো দিন বিসিবি এর দায়িত্বে থেকে কি করলেন একজন ভালো নির্বাচক তৈরি করতে পালেন না??? আর ভালো মানের খেলয়ারের কথা তো ছেরেই দিলাম আগে আপনি আপনার কাজ ঠিক মতো পালন করেন দেকবেন সব এমনিতেই ঠিক হয়ে যাবে।।।।,0,sports
আল্লাহ তুমি আমাদের মাফ করে দেও আর এদের হেদায়েত দাও নাওহলে এদেরকে যা করবা কর,0,sports
এত পণ্ডিতি কথাবার্তা বাদ দিয়ে আপনি দুই দিনের মধ্যে পদত্যাগ করেন। আমি বুঝি নাক্রিকেটের একটা সংস্থার প্রধানের দায়িত্বে এমন একজন লোক আসেন কী করেযার কোনো ক্রিকেটীয় ব্যাকগ্রাউন্ডই নাই! বিসিবির সভাপতি হবেন অবশ্যই কোনো সাবেক ক্রিকেটার। সভাপতি ক্রিকেটের মানুষ না হলে সে ক্রিকেটসংশ্লিষ্ট উন্নয়ন করবে কীভাবে? পাপন শুধুমাত্র আওয়ামী ঘরানার লোক দেখে ওকে সভাপতির দায়িত্ব দেওয়া হয়েছে। এটা কোনো কথা হলো!,0,sports
প্রিয় ইউটিউব পুলিশ অপেক্ষায় ছিলাম অবশেষে অপেক্ষার প্রহর শেষ,0,sports
পাপন এর পদত্যাগ চাই।সাকিব কনো ভুল করেনি।,0,sports
বাংলাদেশ ক্রিকেটকে ধ্বংস করছেন পাপন সাহেব বিশ্বের উন্নত দেশগুলো টিকেটার দের বাঁচিয়ে রাখে আর আমাদের দেশের শালার পুতেরা শুয়োরের পুতেরা ক্রিকেটারদেরকে ফাঁদে ফেলে দে বিসিবির সভাপতি সহ অন্যান্য যারা আছেন সবার পদত্যাগ চাই এরা বাংলাদেশ ক্রিকেটকে ধ্বংস করার চেষ্টা করতেছে,0,sports
বাংলাদেশ খেলা মানি সাকিবুল হাসান সাকিব আল হাসান বাংলাদেশের টিমে খেলবে না সে খেলা দেখে আমাদের কোনো লাভ হবে না আমি ভারত থেকে বলছি আমি সাকিবুল হাসানের বড় ফ্যান আমি কোনদিন দেখিনি এরকম খেলোয়ার খুব কষ্ট হচ্ছে শাকিব বাংলা সিটি মেনেই তার মানে আমাদের টিকিট কাটা ভুল হবে সাকিবুল হাসানের ব্যাটিং আমাকে খুব ভালোলাগে পিছন দিক থেকে যে একটা ছক্কা মারে সেটা আমার খুব ভালোলাগে কলকাতা নাইটাস আর হয়ে একটা ম্যাচ জিতে ছিল এইসব দিয়ে আমার এখনো মনে আছে সেই মেয়েটার কথা,0,sports
পাপনের মুখে 🦶🦶দিয়ে বাইরানো দরকার।,0,sports
খুব সুন্দর খেলছে খুলনা টাইগার,0,sports
মুশফিক সেরা❤❤❤,0,sports
চলছে গাড়ি যাএা বাড়ী,0,sports
মিয়া আপনি এসলে একটা ফালতু এসব আজাইরা খবর দিয়া বকা বানাচ্ছেন মানুসকে,0,sports
বিচার চাই,0,sports
বুজলাম না। কি দেইখা রাছেল কে সিরিজ দিলো।,0,sports
খুব ভালো লাগছে,0,sports
সাবাস খুলনা চালিয়ে যাও কাপ তোমাদেরই,0,sports
চুরি করে ধরা পরলে তার টাকে করে দেওয়া উচিত যেমন সাকিব কেও করা উচিত ।।এরা তো আবার চোরকে করছে।।।মানে চোরে চোরে মাসতুতো ভাই,0,sports
আমি শুধু একটা কথাই বলবো সাকিব যেনো আর বাংলাদেশের জার্সি গায়ে কখনো না খেলে,0,sports
খেলার মধ্যে নাই বাদ দাও,0,sports
পালতু,0,sports
কিছু জারজ সন্তানের বাচ্চা আর কুকুরের বাচ্চা কুলাঙ্গার নাস্তিক কের বাচ্চা রা কমেন্ট করছে তা বুঝা যায়,0,sports
কাজ টা একবাড়েই খারপ হল বাট অনেক মজা পাইছি অনেক হাসছি,0,sports
মুস্তাফিজুর রাএে খেলা পারে না 😂😂😂😂,0,sports
সব কথা থিক,0,sports
এই খবরটা যদি মিথ্যাহয় তাহলে কি মনে করব আপনি ঘালি খাওয়ার জন্য এই খবর বলছেন,0,sports
ভাই লাস্টের এক মিনিট কথা গুলো আমার অনেক ভালো লাগলো,0,sports
মাংগের মুশফিক,0,sports
ভাই আপনার ভিডিও দেখার অপেক্ষায় থাকিযদিও এততো বড় নাটকও দেখিনা।,0,sports
পপনে ক্যাসিনো খেলা ফাঁস হয়েছে,0,sports
নাছির হোসেন কে কি জন্য নেই যে,0,sports
বালের বিচার করে,0,sports
মোবাশ্বের স্যার আপনাকে অসংখ্য ধন্যবাদ কিন্তু স্যার বর্তমান বিসিবির কমিটিতে যারা আছেন তারা উন্মুক্ত থাকা ক্রিকেটটাকেও রাজনৈতিক মোড়কে পেছিয়ে দিয়েছেন একাডেমি ক্রিকেট থেকে শুরু করে দেশের সর্বোচ্চ জাতীয় লীগ পর্যন্ত সবজায়গায় রাজনীতি আর রাজনীতি😌😌😌😌,0,sports
ম্যাচ ফিক্সিং এটা,0,sports
বাংলাদেশের ক্রিকেট কে আজকে থেকে আমি অন্য দেশের ক্রিকেট ভক্ত পাপনের কথা শুনলে বমি আসে কেন,0,sports
আমি আর অক্টোবর তেকে খেলা দেকব,0,sports
সব দিকেই বাংলাদেশের বিপদ আস্তেছে,0,sports
সালারা ইউটিউবে এইসব ভুল নিউজ ছাপিস কেন,0,sports
থাকার জগ্গো নয়,0,sports
মরহুম জিল্লুর রহমান যদি ফার্মেসী দোকানে যেতো আজ এই অবস্থা দেখতে হতো না,0,sports
ক্রিকেট চোক সব ফাইজলামি। সালার ভারত সফরের পূর্বে এইসব নাটক প্রথমত বড়ভাই ভারতকে খুশি করা দ্বিতীয়ত পাপনের দাদাগিরি দেখলাম না ক্রিকেট কি হইবো। ♥♥♦,0,sports
সোম্য সরকার ডেবিটমালায়ন,0,sports
তুই খারাপ সেটা সবাই জানে কিন্তু তুর মা বাবা বোন তো খারাপ নয় তাহলে তাদের কেন গালি শুনালি,0,sports
চামচার অভাব নাই।,0,sports
আমার চেনেলটি সাবক্রাইভ করে ভিডিওর নিচে কমেন্ট করেন বেক পাবেন কসম,0,sports
ভাই আমার মন কি বলতেছে তা বলে বোঝাতে পারব নাবলির পাঠা হলেন সাকিবএর উপদান অনেক বেশি,0,sports
সাকিব আল হাসান ষড়যন্ত্রের শিকার। সত্যিই ভাই আমি অনেক কষ্ট পেয়েছি।,0,sports
রুবেলের কন্ঠ না,0,sports
পাপন জোয়ারিদের নং কি করে পাইলো কারণ সাকিবকে বসানো জন্য কত টাকা খেয়েছে?,0,sports
আসসালামু আলাইকুম মুসলিম ভাই ও বোনেরা।আমি ইসলামিক ভিডিও নিয়ে কাজ করি আমাকে একটু সাপোর্ট করতেন ভালো হতো।,0,sports
ভাই আপনার কথা গোলা অনেক বালো লাগছে,0,sports
টিপু ভাই আপনি কি জানেন যে টিকিটের বড় নেতা আছে ইন্ডিয়ার দালাল যে আপনি তো জানেন না জানলে এত কথা বলতেন না বাংলাদেশকে কিভাবে ডুবেছে পানি খাওয়াবে এদের কামড়ে এটা বাংলাদেশ একটু খাইলে কাউকে ভালো দেখতে পারে না,0,sports
সাকিব তুমার সাথে আছি ভাই,0,sports
আন্দ্রে রাসেলের ফ্রেন্ড গোলা কই,0,sports
কথায় আছে না উস্তাদের মাইর শেষ রাত,0,sports
মজা পাইলামনা।,0,sports
বেটার বেকতি গত বেপার,0,sports
দুঃখজনক ব্যাপার ঢাকা প্লাটন শেষ মাশরাফি মুর্তজা আপনাকে অনেক ভালোবাসি,0,sports
ভাই সাকিব ভাই না আসা পর্যন্ত আমি আর খেলা দেখব না,0,sports
সাব্বিরের বর্তমান পারফরম্যান্স অনুযায়ী বিশ্বকাপ দলে তার জায়গা কি করে হয়🙄🙄,0,sports
ভাই আপনি বলদ নাকী জানেন না আইসিসির নিয়ম অনুযায়ী ম্যাচ ফিক্সিং তার অফার আসলে গোপন না রেখে আইসিসি কে জানাতে হবে আর কোনো কারণে যদি না জানানো হয় তাহলে আইসিসির নিয়ম অনুযায়ী দন্ডনীয় অপরাধ,0,sports
সব সালার পয়সা হলে লুচচামি করে,0,sports
আমি পাপনের সাথে একমত। আচ্ছা যারা আবালের মতো লাফালাফি করছিসতরা বল পাপন কোন কথাটা অযথা বলছে??,0,sports
পাপন হচ্ছে হাসিনা কুটটার!!!,0,sports
ও মাগো শাকিব এতো ভালো হইলো কবে থেকে আমিতো জানি নাম্বার ওয়ান চোর কতবার চুরি করে ধরা পড়ছে তার কোনো হিসাব নেই,0,sports
দারুণ নাচ।,0,sports
কাল থেকে সবাই আন্দোলন নেমে পরো????,0,sports
ভারতকে হারাতে না পারলে সাকিবের মত খেলোয়াড়ের দরকার নেই বাংলাদেশের কারন যখন ভারতকে হারাবে তখনই শক্তিশালী দল হিসেবে প্রমাণ হবে বাংলাদেশ যা সাকিব থাকলে হবেনা,0,sports
অামি শিউর সাকিবকে চাপের মুখে ফালানো হয়েছে,0,sports
আবু হায়দার রনি ভাই কে আমরা সবাই ওপেনার হিসাবে দেখতে চাই,0,sports
বেশি বাড়াবাড়ি,0,sports
এবার খুলনা টাইগার্স ইতিহাস গড়বে এবার ট্রফি খুলনা টাইগার্স জিতবে কে কে সহমত,0,sports
মুশফিকের দোষ,0,sports
ভালোবাসি সাকিব ভাই কে,0,sports
বিশ্ব এটাই চেয়েছিল সাকিবকে পেছনে ফেলে দিতে 😓😓😓😓,0,sports
ইসলামের উপর কে দিয়ে শুরু হলো। মুসলিম সবাই এক হলে কেউ কিছু করতে পারবে না। ইনশাআল্লাহ,0,sports
যদি চাইলেই পাইতো তাহলে আন্দোলন করত না। নিজের সাফাই গাইল পাপন সাহেব। ক্রিকেট ভালবাসে কিন্তু পাপন সাহেব কে না।,0,sports
ভাইরে পাপন রে হাত মেরে মাল খাওয়াইতে ইচ্ছা করে,0,sports
মাদারটোস্স,0,sports
সুন্দর ভিডিও দেকতে ক্লিক করুন,0,sports
সবাই এই বন্যপ্রাণী টিকে রিপোর্ট মারুন।,0,sports
গনেশে মতো পাপনের পেটা ফুলে গেছেএত দুর্নীতি আল্লাহ সয্য কারবে না।।।।,0,sports
পা পোন্দার পানখা রাই ভিডিওতে ডিজলাইক করে।,0,sports
বস্তির ছেলের হাতে টাকা আসলে যা হয় আরকি,0,sports
এই গুলো ফাজলামো ছাড়া আর কিছু না।,0,sports
কি কথা দেখোমরা গরু হাটানোর মত কখা,0,sports
গালি দিলে কি হইছে পাগল সব,0,sports
কোন সময় যে বলে ফেলে এটা বিএনপির ষড়যন্ত,0,sports
পরবে মানে পরে গেছে সাকিব না থাকলে খেলাই হইতো দেখব না,0,sports
মহিলাদের ধোকা খুবই মারাত্বক,0,sports
নাছির তুই যে একাজ করবি কখনো কেউ বাবতে ও পারেনাই। নাছির তর মনে হয় জরমের ঠিক ছিলো না তাই এ কাজ করছত।,0,sports
সাবিবর এক নাম্বার মাগিবাজ,0,sports
গত বছর কুমিল্লায় কাপ নিলো এবার ইমরুলের হাতে চট্টগ্রামে কাপ যাবে প্রিয় বস ইমরুল ভাই,0,sports
গাঁজাখোররে লাথি মার চামচা হালার হালা,0,sports
ভাই যদি আন্দলোন হয় একমাত্র উপায় রাজি আছি দেশকে ভালোবাসি দেশের ক্রিকেট কে ভালোবাসি । আর সাকিবের সাথে আছি 💙💚💜,0,sports
নতুন কমিটি দেওয়া হোক,0,sports
শাকিব শাস্তি পাওয়াতে অনেক ক্ষতি হবে বাংলাদেশের।,0,sports
...ভাই সহমত প্রকাশ করছি আপনার সাথে ....অসংখ্য ধন্যবাদ আপনাকে,0,sports
শাকিব প্রতিবাদ করেছিলো বলেওর বিরুদ্ধে এই ব্যবস্থা,0,sports
মদ খায় সালারপুত মদ না খাইলে তোগো বুদ্ধি হইবো না।,0,sports
নাইছটিফছ,0,sports
এটা কোন ধরনের মজা ভাই,0,sports
কাছের মানুষ কেউ আপন হয় নাকেউ কেউ পাপন ও হয় 🤣,0,sports
হাইলাইটসে উইকেট দেখানো হয়না। জাস্ট র‍্যাবিটহোল থিংস,0,sports
দিনে খেললে বল ভালো হয়ছে 😂😂😂,0,sports
আসসালামু আলাইকুম আমি ভাই ক্রিকেটভক্ত নয় ঠিক আছে কিন্তু তারপরও আমি খুব খুশি হলাম সাকিবুল হাসান উনি বলছেন ইংল্যান্ডে খেলবে তারপর আমি খুব খুশি হয়েছি আমাদের বাংলাদেশের হয়ে খেলার কোন দরকার নেই কারণ কোন সম্মান পান নাই আপনি ঠিক আছে ভাই,0,sports
সব টাকা পাপুআপু খাইলে কেমনে দিবে খেলোয়াড় দের। তার দিন শেষ হলে আর খাবে না,0,sports
অন্য কাউকে সুযোগ দিয়ে তুমি এখন আস্তে পার।,0,sports
সাকিব পুরোপুরি ষড়যন্ত্রের শিকারআর এ ষড়যন্ত্রের পেছনে মূখ্য ভূমিকা পালন করছে স্বয়ং বিসিবি বোড কর্তারাইআমরা পাপনের পদত্যাগ চাই,0,sports
আমার মত কে কে ক্রিকেট ভালোবাসেন? 💖💖💖তারা লাইক করুন👇👇👍👍,0,sports
তাদের কে পাগলের উপাদিদেও হক,0,sports
"আসলি পকিরের পু, ,,এখন টাকা আলা, ,, ছোট মনের লোক তো তাই,,,",0,sports
কিছুই যখন হয়নি তখন হ্যাপির কথা বলার সময় ঘামতেছিলেন কেনো রুবেল...??,0,sports
একটা লাইক মানে পাপনের গালে একটা করে জুতার বাড়ি 👇👇👇,0,sports
আপনি কথাটা মিথ্যা এটি একটি গুজব আমি হান্ডেট পার্সেন্ট সিওর,0,sports
পাপর্ন 🤣🤣,0,sports
"লাশ কবরে রাখার দুয়াটি হয়নি,,,,ফালতু",0,entertainment
ভাই এই মেয়ে শমি কায়চারদের মোত হবে। পরে দেখবেন বুড়ো বয়সে এদের পাশে কেউ নেই,0,entertainment
কে হবে মা চুদ রানা। এখন সব হারায়া হইসে কানা।,0,entertainment
"হায় রে বাংলাদেশ এই কি ছিল ছাওয়া, আমাদের মহাননিজ স্বমহিমায় প্রতিষ্ঠিত,",0,entertainment
এসব জাজদের নাটক দেখা করে দাও।,0,entertainment
শেষমেষ মেয়েটাকে কি পাওয়া গেল না,0,entertainment
কে আমাদের পাঠিয়ে ছেন আর কেন বা পাঠানেল এক বার ভাবুন এসো আমারা সভাই পাঁচ ওয়াক তো নামাজ পড়ি আল্লাহ তালা আমাদের নামাজ পড়ার জন্য তাগিদ দিয়েছেননামাজ বেহেশতের চাবিকাঠি,0,entertainment
নাইস ড্যান্স খুব ভাল লাগল,0,entertainment
গু 😆😂🤣,0,entertainment
মামুন ভাই পতিতা নাটক বাদ দিয়ে অন্য ভালো নাটক নিয়ে আমাদের মাঝে আসেন।,0,entertainment
ছবি খুব ভালো লাগে কে,0,entertainment
থ্যাংকস ফর ইউ,0,entertainment
এসব খারাপ মেয়ের কোন পোস্ট আপনেরা করেন না প্লিজ,0,entertainment
কে কে এই ছবি দেখতেছেন,0,entertainment
আপনারা একটা ফায়ুল মার্কা কারন ছবির গান গুলা মাউথ করছেন কেন?,0,entertainment
খারাপটা রে বাংলাদেশ থেকে বের করে দেয়া উচিত,0,entertainment
পরের পর্ব কবে দিবেন???,0,entertainment
ভাই আপনি একটা জিনিস,0,entertainment
নেটেক চবিফেলবাংলা ছবি কাছে,0,entertainment
এরোকম আরো হট চাই,0,entertainment
নষ্টা মেয়ে মুভিটা দিন,0,entertainment
"ভাই তুমি কিন্ত ভাগ্য বিড়ম্বনা নাটকটা এখনো আপলোড দাও নাই,বারংবার বলার পরেও।",0,entertainment
দরকার সিফাতুলা দিয়া গালি দেওয়া দরকার,0,entertainment
"অগ্নি স্বাক্ষর, অসাধারণ সুন্দর মুভি কাঞ্চন ভাইর।",0,entertainment
শাবনুরের সাথে মানায়নি নায়ক কে,0,entertainment
জিন ছাড়ানো দেখুন হাফেজ ক্বারী মাওলানা মোঃ আবু সাঈদ খুলনা যোগাযোগ নাম্বার ০১৯৮৫২৯৮৪১২/০১৭৫৯২৯১০৭০,0,entertainment
রিয়াজ মানেই রুমান্টিক,0,entertainment
মন্ত্রী নজর কিন্তু ঐ জিনিস দিকেই বিয়া করতাছে🤣🤣🤣,0,entertainment
ভালো লাগছে এই জুটি আরো দেখতে চাই!!!!,0,entertainment
বাংলা সিনেমা ইতিহাসের সেরা নায়ক সালমান শাহ্। হুমায়ুন ফরিদী তো কালজয়ী অভিনেতা....,0,entertainment
খুব সুন্দর মুভি,0,entertainment
গল্পের ভিতর গল্প,0,entertainment
ধন্যবাদ ভাইয়া । মানিক রতন ছবিটি upload দিন ।,0,entertainment
বাহ্ বাহ্ ভালতো আজ সকালেই দিলেন,0,entertainment
এই সব পাগল ছাগল দিয়ে কি নাটক হয়,0,entertainment
বাড়ি ওয়ালার মেয়ে তানাজ তুমি যদি এই পোস্টটা দেখে থাকো তাহলে মোটর ছাড় জলদি কলে পানি নাই। অনেক্ষন টয়লেটে বসে আছি। 😲,0,entertainment
দেখার মতো একটি ছবি<br />ছবিটি শেষের দিক দেখে চোখে পানি এসে গেল।,0,entertainment
ইরিনের আরো মুভি করাউচিত ছিলো,0,entertainment
আল্লাহর মেহেরবান শেষ হয়ে গেল?,0,entertainment
ছুটেরে ঘোড়া ছুটেরে ঘোড়ার পা টা খোঁড়ারে ঔ ঘোড়া তোর নাম কি ওরে বাবা টিকটিকি।।।।।।অনেক ভালো লাগলো শেরা নায়ক মুভি টা আপনারাও দেখেন ভালো লাগবে,0,entertainment
এই বিচারকদের যেই ভাব দেখে হাসি পায় ভাব দেখে মনে হয় এদের চাইতে ভাল বিচারক আর নাই,0,entertainment
"কিছু বলার ভাষা হারিয়ে ফেলেছি, অসাধারন একটি ছবি অসাধারন ধন্যবাদ তৌকির আহমেদ ভাই এই রকম একটা সুন্দর ছবি উপহার দেওয়ার জন্য।",0,entertainment
"আজও গরীবদের ওপর বড় লোকদের এই ধরনের অত‍্যাচার চলছে, শুধু নিয়মটা অন্য রকম ।",0,entertainment
সাবনাম ফারিয়া আর দাড়িওয়ালা ভেড়া মার্কা কি জাজ এর কাতারে পরে জাজ গুলার মধ্যে কোন শালিনতা নেই এই ভাবে অপমান করার কোন অধিকার নেই তাদের। করেন,0,entertainment
সাকিবের ছবি আগেই অনেক ভালো লাগতো,0,entertainment
কথা সুনা যাইনা নাটক আবার এত ভালো,0,entertainment
আমার খুব সক তুরে সুদার টাকা দেমু জত লাগে,0,entertainment
সবার অভিনয় ভালো হয়েছে। তবে ফজলুর রহমান বাবু ওশহিদুজ্জামান সেলিমের অভিনয় অসাধারণ!,0,entertainment
"আমি কোলকাতায় থাকি,,,,,,my favourite actor apurbo........I love you boss",0,entertainment
চাইনা তোমার দেহ চাইনা তোমার মন দেখবা আমার ধন মম😂,0,entertainment
আমি নাটক পছন্দ করি,0,entertainment
মন খরাপ করে কি লাভ,0,entertainment
আমার মনে হয় হিরো আলমের নায়িকা হওয়ার যোগ্য ওর এখনো হয়নি,0,entertainment
দায়িত্ব পেলে বোবারাও নিজেদের ক্রিয়েটিভ যাহির করার চেষ্টা করে।,0,entertainment
আনেক ফানি,0,entertainment
এমন আবেগ ময় মুভি আর হবে না এই ভবে।,0,entertainment
জুই করিম রে বাদ দে নাটক থেকে একটা হিজলা লও তাও ভালো,0,entertainment
এরকম খারাপ ভিডিও,0,entertainment
তুমি ফুল আমি কলি নামবার দাও কথা বলি +৯৭৩৬৬৯৯২১৮৬,0,entertainment
অনেক দিন পর শাবনূর আপুকে দেখে ভালো লাগতেছে আরো শাবনূর আপুর নতুন মুভি চাই,0,entertainment
তোদের গান শুনে আমার। আর বাঁচতে ইচ্ছে করছে না।,0,entertainment
টেনশন মূভি টা কি নতুন না পুরাতন,0,entertainment
দুধের নাচ দেখি,0,entertainment
কি এতে তো কিছু নাই,0,entertainment
দারুন হাসির নাটক,0,entertainment
এইটা কোন ছবি হল নাকি,0,entertainment
"যৌতুককে না বলুন,,,যৌতুক নিয়ে বিয়ে করলে কখনোই একটি সংসারে শান্তিতে বসবাস করা যায় না,সুতরাং আমরা যৌতুক নেওয়া থেকে বিরত থাকব,,,,নারীদের প্রতি যৌতুক না দেওয়ার দায়ে নির্যাতন করা বন্ধ করুন,,,ধন্যবাদ সবাইকে",0,entertainment
আমি আমিনখানেরসাথে শাবনুরের ছবি ছাই,0,entertainment
মোসারফ ভাই বেস্ট,0,entertainment
এরকম ছবি চাই সব গুলো পুরানো ছবিগুলো দেখতে খুব ভালো লাগে এখন নতুন ছবি আর ভালো লাগেনা পুরানো ছবিগুলো,0,entertainment
উপসসস..... লিরিক্স পুরাই কাপায় দিছে :o,0,entertainment
ভিডিও তে অনেক বেশি ছিল,0,entertainment
বিশ্বাস করেন ভাই এক হাজারের উপরে কমেন্টস দেখলাম কেউ বিচারক গুলারে ভালো বলল না শবনম ফারিয়া জাকিয়া বারী মম ওদের দিয়েছে বিচারকের আসন আজ যদি মাসুদ রানা বেঁচে থাকত যদি দেখতো জাকিয়া বারী মম শবনম ফারিয়া বিচারক তাহলে সে নিশ্চিত মারা যেত আর আবাল দুইটা তিনটার কথা নাই বললাম ওদের মধ্যেই তো কোনো ভালো লক্ষণ নেই তোরা ভালো মানুষ কিভাবে বের করবি ওদের ভাব দেখলে মনে হয় অস্কারজয়ী অভিনেত্রী অভিনেতা চ্যানেল আই কে বলতেছে বাংলাদেশ সে কি ভালো মানের বিচারক নাই ওদের মতো কুলাঙ্গারদের দিয়ে এই ধরনের অনুষ্ঠান করাইতেছেন,0,entertainment
রিয়াজ আবারও আসুক,0,entertainment
"যদি পৃথিবীর সব গোলাপ প্রতিদিন একটা করে তোমাকে দিয়ে বলি আমি তোমাকে ভালবাসি ,সব গোলাপ শেষ হয়ে যাবে ..তবুও আমার ভালবাসা শেষ হবে না ..হয়তো আজও আমার ভালবাসার গভীরতা বুঝতে পারো নি ...!!+97466982508",0,entertainment
ভাই তালি টা কম হইয়া গেলো।😣😣😣😣 আরো অনেক তালি দরকার ছিলো। আপনার উপর আমার রাগ হইতাছে😥😥😥😥😫😫😫,0,entertainment
খুব মনে পডে নায়ক মান্নার কথা,0,entertainment
নিলয়র নাকগুল অনেক ভাললাগে।,0,entertainment
সেশে না দেখলে তো মজাই পাওয়া যায় না তো বাংকি টার কি খবর সুটিং কি হবে কি না না এই পর্যন্তই সেশে 😔😔😟😟☺😊😊🤔🤔🤔🤔🤔🤔🤔🤔🤔🤔🤔🤔🤔🤔🤔🤔🤔,0,entertainment
ভুয়া অনুষ্ঠান এই ধরনের বিচারকদের শাস্তির আওতায় আনা হোক,0,entertainment
আমাদের বাংলাদেশের নাটক পোরা পৃথিবি জোরে শেরা তাই জত বার নাটকটা দেখি ততবারি ভাল লাগেধ্যনবাদ সবাইকে,0,entertainment
মান্না ভাই বাংলা চলচ্চিত্রের ইন্ডাস্ট্রি।,0,entertainment
"আমি মোশাররফ এর বড় ফ্যান। মোশাররফ - তিশা সেরা জুটি, কে কে একমত আছেন!",0,entertainment
আমার চারজনভাইআছেকিন্তু বড় দুইভাইকোন দিনখুঁজ খবর নেই না আমি আমারভাইদেরঅনেক ভালবাসি বিশেষ করে ছোট ভাইয়ের,0,entertainment
এটিএন মিউজিকের ব্যানারে উনার আরো তিনটা অডিও অ্যালবাম আছে যদি পারেন তো ওগুলো দিলে আরো ভালো হয়,0,entertainment
আমার হিরো রুবেল,0,entertainment
দেখেছি আসলেই খুব ভয়ানক ছিলো 😷,0,entertainment
নিকিটবিযিঅ,0,entertainment
অনেক দিন পর একটা বাংলা ছবি দেখলামভালো লাগছে,0,entertainment
সুন্দর হইছে,0,entertainment
মইন্না ভাল্লাগছে,0,entertainment
এক বছরে দশ লক্ষ লোক ও দেখে নাই...ইয়াক থু এই দেশের মাইনষের রুচির উপ্রে...আমরা ভালো কনটেন্ট ডিজার্ভ ই করিনা আসলে...,0,entertainment
পালতু পরিচালক পালতু মুভি,0,entertainment
এই নিয়ে তিন বার দেকলাম ভিডিও টি আসলেই ভাবতে অবাক লাগে এই পৃথিবী।,0,entertainment
বাংলাদেশি নাটক অনেক সুন্দর কেন যে মানুষ ইন্ডিয়ান চ্যানেল এর পিছনে সময় দেয় জানিনা,0,entertainment
আমার অনেক ভালো লাগে,0,entertainment
কইজে পায় এইটা কি নায়ক,0,entertainment
আল্লাহ তোদের টা বাঁশ একসাথে দিবে ।।,0,entertainment
আমাদের মিউজিক টেস্ট যে কত খারাপ তা এই গান এর ভিউজ দেখলেই বোঝা যায় 😑,0,entertainment
গঞ্জিকা পাতার জুস খাইলে যা হয় আরকি।।। এইসব ফালতু আর্টিস্টদের জন্য অনেক ভালো আর্টিস্ট উঠতে পারেনা। লিরিক এর অর্থ হয়তো এরা নিজেরাও জানেনা 😒,0,entertainment
গানের বানী আর মনের বানী এক না হলে কি এই গান আসে,0,entertainment
"এই ভিডিওটা অনেক ভাস্তবিক<br />মেয়ে প্রথম যা করছে সেটা সে পেটের দায় করছে,<br /><br />তবে দ্বিতিয় বার যারা সংসার ভাঙ্গার ভয় দেখিয়ে প্রতারনা করে নিজের ফায়দা<br />আছিল করতে চায় <br />আল্লাহ তালাহ্ যেনো তাদের আজীবন জাহান্নামের আগুনে পুড়ান,<br /><br />মেয়েটার হাত জুড় আকুতি<br />দেখে আমার দুই নয়নে অশ্রু ধরে রাখতে পারলা না,<br /><br />ওই সব বোনদের এইরকম বীর সাহসী স্বামী যেনো তাদের ভাগ্যে থাকে,<br /><br />এইরকম নব দম্পতিদের জন্য অনেক দোয়া ও ভালবাসা রহিল।",0,entertainment
নাটকের ভিতরে আওয়াজ কিসের আওয়াজ দিকে একটু খেয়াল দেবেন,0,entertainment
বাংলার বাঘ একটাই নায়ক জসিম,0,entertainment
ছি এগুলো কি নিজের ছেহারা নাইঢক তোঘরে পাইলে ঘন্ট জুতা বারি মারতা এই টাই মাসুদ রানা কেরেকটার,0,entertainment
ভাইয়া এতো দিন বন্ধ রাখছিলেন।।,0,entertainment
আই ফিল্ম দেখে আমারচোকেএখন জল আসে।,0,entertainment
অনেক সুন্দর হয়েছে নাটকটা।,0,entertainment
ওমর সানি অভিনীত জানের দুশমন মুভিটি আপলোড দেন ১৯৯৩=১৯৯৪,0,entertainment
"মা আমার জান,মা উপর কেউ না",0,entertainment
আমরা আসলে কোনো খারাপ স্বভাবের মানুষকে ভাল হওয়ার সুযোগ সৃষ্টি করে দেই না বাস্তব সত্য কথা ? শত চেষ্টার করলে ও সমাজ ব্যবস্থা আবার তাদের পিছিয়ে দেই কলুষিত করে আবার চরিত্র ..?<br />আসেন আমরা সবাই একসাথে একটা পরিবর্তনের স্লোগান তুলি ??,0,entertainment
নষ্টনায়িকা,0,entertainment
হৃদয়স্পর্শী গানের কথাগুলোর সাথে সুরের এতো বেশি মিল বন্ধন যা একাধিকবার শুনতে বাধ্য করা হলো।❤,0,entertainment
চম্যকার মুভি রোবেল ভাইয়ের সাকিব তো রোবেল ভাইয়ের কাছে কিছুই না,0,entertainment
বলদ,0,entertainment
"আর কোন কাম নাই,,,,",0,entertainment
এই নায়ক এখন মনে হয় ডুবইতে কনট্রাকশন কম্পানিতে কাজ করে আর কি করবে,0,entertainment
নতুন নায়ক দের সাথে ছবি করে শাবনুরের কোনো ছবি হিট&#39; হয় নাই। যেমন এটাও সুপার ফ্লপ। কোন নায়কের ই সেরা ছবির নায়িকা শাবনূর নয়। এই ছবির নায়ক কে তো শাবনুরের ছেলের মতো মনে হয়। ময়ূরীর ছবির কোয়ালিটি ও এর চাইতে অনেক ভাল হয়।,0,entertainment
দুনিয়ার ফাউল ট্রেইলার...🤬<br />এইটাকি নাটকের প্রমো নাকি একটা মুভি প্রমো সেটা বুঝতে বুঝতে প্রমো শেষ হয়ে গেল...🤒<br />এটা নাকি একটা মুভির প্রিন্ট...🤮<br />হাস্যকর সত্যি হাস্যকর...🤮,0,entertainment
"এই রকম ছিনেমা আর কোন দিনও হবেনা,কারন সালমান শাহ আর নেই তাই,সালমান শাহ তোমাকে অনেক মিস করি,আর দোয়া করি,আল্লাহ তোমাকে বেহেশত বাসি করে যেন।আমিন",0,entertainment
"পশ্চিম বাংলার মত বাংলাদেশেও চলছে হিন্দি এবং উর্দু আগ্রাসন, জয় বাংলার পরিবর্তে আমরা একদিন বলতে হবে জয় হিন্দ কিংবা পাকিস্তান জিন্দাবাদ ।",0,entertainment
এই রকম মুভি আর হবে না,0,entertainment
বাই আল্লাহা আপনার হেফাজত করুন,0,entertainment
আব্দুল আজিজ ভাই কে অসংখ্য ধনব্যদ ড্রেসটা চেঞ্জ করলে আরো ভালো হয়তো ভাইয়া,0,entertainment
পাচ ওয়াক্ত নামাজ পড়লে মন শরীর ভালো রাখেন আল্লাহ।।।,0,entertainment
বাংলাদেশের নায়ক এবং নায়িকার শিল্পীরা সবাই মৃত্যুর আগে চলার জন্য বাংলাদেশ সরকারের কাছে অনুদান চায় ওরা লাখ লাখ টাকা কামিয়েছেন একটাকাও দেখাতে নাই কারণ এ টাকা হল হারাম এইজন্য ওদের শেষ বয়সে এই করুণ অবস্থা হতে হয়,0,entertainment
ইমুতে কথা বলার কেও আছো? রাতে অনেক মজা করবো।,0,entertainment
গালি বয় রানা রে মাসুদ রানা করা হোক,0,entertainment
বাংলা দেশে কি ছেলের অভাব ছিলো সিশনাগ কে দেখেতো তাই মনে হলো,0,entertainment
অসাধারণ একটা গল্প ভালো লাগছে,0,entertainment
নাউচ,0,entertainment
আঙ্গো বাড়ি নোয়াখালী,0,entertainment
"এক সময়ের হিট নায়ক আমিন খান,,কিন্তু দুঃখজনক এই ছবিতে তার অবদান কিছুই নাই আমার মনে হচ্ছে,,<br />ইচ্ছে ছিলো দেখবো কিন্তু আর দেখব না😏😏",0,entertainment
পাঁচ ওয়াকত নামাযে শালমানেৱ জনন দোয়া কে কে কৱে ।,0,entertainment
অনেক সুন্দর হয়েছে সাকিব খান সেই রকম হয়েছে,0,entertainment
ছি একজন শিক্ষিত মানুষ এমন বাজে ভাবে বিহেব করতে পারে তাও আবার অন স্ক্রিন জানা ছিলোনা আপনারা কিভাবে আসছিলি মনে নাই।নিজদের অতীত একবার মনে করে বিচারকের আসনে বইসেন👿👿,0,entertainment
"আমিনের সাথে কি আবার???<br />মিসা কে যে ভাবে ট্রেইলারে দেখালো তার একশো ভাগে ৫ ভাগ ও দেখায় নি,,<br />তার মানে কি আমিন খান অথিতী চরিত্রে??<br />আর কি আমিন খান কে নায়ক হিসেবে দেখতে পাবোনা??/",0,entertainment
"হাহাহা-- মজা পেলাম, একটা বাচ্চা হবার পরও কোনো মেয়ে ভার্জিন থাকে।",0,entertainment
এত সুন্দর শিল্পী কোথায় পাইছেন ভাই,0,entertainment
আমি ওর অনেক গান দেখেছি ওরে অনেক বালো লাগে আমি বিয়া করমো সৌদি আরোব তেকে বলছি নেওয়াজ ইমো নাম্বার 9660571985975,0,entertainment
অনেক অনেক ভালো লাগলো,0,entertainment
কিনে দিব তোকে আমি প্রাইভেট কার আমার পাশে দুলাভাই আমি ড়্রাইভার,0,entertainment
খেলা হপ্পে,0,entertainment
ভাই রুবেল ভাই এর লড়াই মুভি দেখতে চাই,0,entertainment
দারুণ দিলে,0,entertainment
ভাই আপনার কাছে একটা অনুরোধ করছি যদি পারেন তাহলে ঈদের দিন একটা আন কমান ছবি দেবেন যা অন্য কোন চেলেনে নাই,0,entertainment
অনেক সুন্দর হয়েছে রাজাবাবু ছবিটা রাজাবাবু টু ছবি দেখার জন্য কে কে অপেক্ষায় আছো প্লিজ কমেন্ট।,0,entertainment
আগের ছবির কাহিনী গুলো কত সুন্দর???. <br />সাকিব আসলেই লিজেন্ড।।,0,entertainment
আফ্রিদির এমন অভিনয় এই প্রথম দেখলাম! 😍 <br />কিছু বলার নেই। 🔥<br />অসাধারণ 😮👌,0,entertainment
ভাই আমিন খানের ছবি আরো দেন,0,entertainment
আমার দেখা সকল সিরিয়াল গুলোর ভেতর জান্নাত সিরিয়ালটি সবচাইতে বেশি প্রিয় ও সবচাইতে বেশি পছন্দের সিরিয়াল এই সিরিয়াল এর বর্ননা এক কথায় বলা সম্ভব নয়,0,entertainment
"আমি একটা কথা বলতে চাই,,,, যে এরা তো আমাদের মত মানুষ,,, এরা তো আমাদের মত সমাজে বাছতে চাই,,, আজ যদি এরা আমাদের আপন বোন হত,, তাহলে কি এইসব করতে দিতাম না কোনো এইসব করতে দিতাম না,,, যার যার বাবা মা আছে তারা মনে নেনো কারন এরাও বাছতে চাই,,,",0,entertainment
আমার প্রিয় মান্না ভাই,0,entertainment
আমি তো মমর নাটকই দেখি না 😡😡,0,entertainment
বোরকার নিচে হাপ পেন পরলে তুই দেখতে তুই পাগল নাকি আমার তো মনে হয় তুই পাগল হয়ে গেছিস ফালতু মেয়ে,0,entertainment
"উদ্দেশ্য বিহীন গন্তব্য ও দূর্ঘটনা থেকে ভাল কিছু আসা করা বোকামি,বর্তমান মুসলিম নাস্তিক হচ্ছে ইউরোপের উন্নত জিবনের আসায়,নাটক সিনেমা নির্মাতারা তাদেরই মন জোগায়,অর্থ কষ্টে থাকা এ টি এম সামছুজ্জামানরা এই সব কাজে জড়িয়ে যায়, এই ব্যক্তির নিজ মুখে বলা কথা,তিনি বাবার অবাদ্র সন্তান ছিল,তাকে ওকিল বানাতে চেয়েছিল তার বাবা,সুখ শান্তি কি জিনিস ওনার নসিবে মেলেনি,ওনার কোন সন্তান ওনাকে শ্রদ্ধা করে না, ওনার এক ছেলে অন্য ছেলে হত্যা করেছে, সে অনেকের জানা।(ইসলাম নিয়ে মজা করার ফল ভাল হয় আমার জানা নেই, কেউ জানলে জানাবেন আমাকে)।",0,entertainment
ওর কথা গুলী বডি আমার মতন তাই ভাললাগে,0,entertainment
সালারা কি রকম বেয়াদব মাসুদ রানা মুভি আসলেও ঐ মুভি আর দেখবো না কি রকম অপমান করছে ছেলে গুলারে 😠😠😠😠,0,entertainment
খেতার চরিত্র,0,entertainment
রাকার মধ্যখানে খাটি সোনা আছে।,0,entertainment
আমার মোবাইল ফোন কেনার তারিখ পর্যন্ত অবসর উত্তর ছুটি ভোগ করতে হয় তা আমরা অনেকেই হয়তো বার পঠিত মন্তব্য করুন জবাব বাতিল আপনি আপনার সাইটের ভিজিটর বাড়ান হও,0,entertainment
এটা কি ছিলো?? গান নাকি অন্য কিছু?,0,entertainment
সুন্দর হয়েছে ধন্যবাদ সবাইকে,0,entertainment
সত্যিই অসাধারণ ।শিক্ষার অনেক কিছুইএখানে আছে ।ধন্যবাদ চঞ্চল কে।,0,entertainment
প্ররিচালক একটা হুমার গানাম,0,entertainment
আশা করি আর দীর্ঘ অপেক্ষায় রাখবেন না। আমাদের ভালো রাখুন আপনারাও ভালো থাকুন।,0,entertainment
তুই আর নাটক দিসনা।,0,entertainment
এই দিন গুলো আবার যদি ফিরে আসত,0,entertainment
"আসুন আমরা সবাই পাঁচ ওয়াক্ত নামাজ আদায় করি জামাতের সাথে 🤲🤲 কারণ আমরা সবাই মুসলিম।। আপনার মা-বাবা কে আপনার সাথে রাখুন বেশি বেশি মা-বাবার খেদমত করুন,,, আপনার মা-বাবা কে কোনো সময় অবহেলিত করবেন না,,,",0,entertainment
হি হি হি পাগল মনে হয়,0,entertainment
এদের যারা ভালবাসবে তারা পরকাল হারাবে।।। আলেম এদের থেকে আমাদের সতর্ক করেছেন দেখুন : -- মৃত্যুর পূর্বে সতর্ক হন।,0,entertainment
শাকিব খানের নতুন নতুন গান বা মুভির জন্য আমার মত কে কে পাগল???,0,entertainment
হুমায়ুন ফরীদি পরেই শহীদুজ্জামান সেলিম।,0,entertainment
গ্রুপে ভিডিও লিংক দিছি। এবার তোর গুষ্ঠি উদ্ধার হইবো 😂😂😂,0,entertainment
বালের নাটক <br />মেগাবাইট নষ্ট এবং সময় ও নষ্ট,0,entertainment
কোবাইন্না খালা মনি😠😠😠,0,entertainment
সত্যিই অতীত বড় মধুর এবং বেদনার,0,entertainment
মজা হবে আর আল্লাহ পাক কি যে করবে সেই জানবে,0,entertainment
"ভাই অনেক ভালো একটিং করে,,, ভাই এর নাটক ভালো লাগে মজা পাই",0,entertainment
এই মহিলা সব সময় উপরের দিকে তাকিয়ে কথা বলছে কেন??কেমেরা যেদিকে সেদিকে তাকাবে।আর এত ভাব।ইউটিউবার হয়ে মনে হচ্ছে নায়িকা হয়ে গেছে। কত কিছু নাকি তার ফেস করতে হয়😂😂।বিয়ের প্রস্তাব। নায়িকারা তাহলে কেমন করে।।যে চেহারা তাও।হাসি পায় এসব ভিডিও দেখলে।😂,0,entertainment
বালের মুভি আপলোড দাও,0,entertainment
আমি বাংলাদেশী সব নাটক খুব পছন্দ করি আমি ও সিনিয়ের ভাই দের মত দেশের জন্য কাজ করতে চাই যদি একটা সুযোগ পাই,0,entertainment
"হৃদয় নারা দেওয়া ছবি, অসাধারণ",0,entertainment
মিলটা দিতে আরো সুন্দর হত,0,entertainment
দেখা শুরু করলাম যাই হোক,0,entertainment
অনেক অনেক ভালো লাগছে মুভিটা এই রকম মুভি আরও আসা করি পামু,0,entertainment
এই মুসলিম দেশে অাউলিয়ার দেশে এই সব নাস্তিকের যাইয়গা নেই। মেয়েরা চাই তার স্তন কে ডেকে রাখতে সে বলে স্টাইল। হাজার হাজার ছেলেদের দৃষ্টি নষ্ট করছে। নাস্তিক কে বাংলাদেশে টাই দেওয়া হবেনা হবেনা। আমি যদি সানাই কে পাই অাল্লার কসম সালিকে এমন করব,0,entertainment
আমার চখ দিইয়া পানি আসে দেখলে ফাসি,0,entertainment
"শুধু হাত পা নিয়ে জন্ম নিলে কি মানুষ বলে তারে,,, মানুষ হয়তে কইজনে পারে",0,entertainment
ফারিয়া একটু পর পর মোবাইলে কি সোনা ডা দেখে,0,entertainment
"এটা তামিল মুভির নকল কপি।তামিল মুভির লিংক দিলাম দেখেন আরও ভালো লাগবে। <a href=""https://www.youtube.com/watch?v=YmPQtzUM5zg&amp;t=7817s"">https://www.youtube.com/watch?v=YmPQtzUM5zg&amp;t=7817s</a>",0,entertainment
আমি দুইবার হলে গিয়ে দেখছি,0,entertainment
এই মুভির নায়িকার কী? আর কোনো মুভি আছে!,0,entertainment
ভাগ্য ভালো আমি অডিশনে পার্টিসিপেট করি নাই মাইরা টেংরি ঝুলায় দিয়াসতাম!আপনারা জাজ হইছেন আপনারা মাসুদ রানা কয়টা পড়ছেন জানতে ইচ্ছুক আমার পুরা সিরিজ পড়া আছে!ম্যানার্স ঠিক করেন নতুবা ঘাউড়া কোন প্রতিযোগির হাতে পড়লে মাইরা চাপার হাড্ডি ভেঙে দিবে!!😑😑,0,entertainment
আমিন খান হিট সুপার হিট নায়ক।,0,entertainment
ওরে ভাই আমার জিবনে দেখা চরম একটা ইন্টারভিউ খুবি খুবি মজা পাইলাম 😂😂😂,0,entertainment
কুত্তা মরার পর ফেরেশতা আসলে বলিস মাই লাইফ মাই রুলস,0,entertainment
একটি শিক্ষামূলক সিনেমা বলা যায় ১০০./: যে যেমন তাহার কপালে জুটেও তেমন=শুধু গান গুলই খারাপ তাহা ছারা সিনেমার সবটুকুই কাহিনি খুবি ভাল লেগেছে সেই রকমের একটা মুভি দেখলাম সিনেমাটি দেখার আগে ভাবতাম মনে হয় তেমন কোন কাহিনি নাই দেখার পরে সে ভুল টুকু ভাংল=অলদা বেস্ট,0,entertainment
হা হা হা।।।,0,entertainment
এই ছবির সব গান গুলো লোড দিলে খুশি হবো।,0,entertainment
শুরুর থার্ড ক্লাস নাচ দেখে বুঝলাম এটা বাংলাদেশের শো,0,entertainment
ঘোলা ছবি উপরে চকাচক ভিতরে ঘোলা,0,entertainment
ডিজিটাল সময়ে<br />চিঠি আদানপ্রদান নেই।<br />চিঠি আদানপ্রদানের ভালোবাসার কাব্যিক বিশ্লেষণ টা অনেক সুন্দর।<br />পোষ্ট অথবা চিঠির কাব্যিক ভালোবাসা টা এখন হয়ে গেছে সোনালী অতীত।,0,entertainment
"একদিন সাদা কাপড় পড়ে,<br />যেতে হবে অন্ধকার কবরে ।<br />তোমার সব কিছু পড়ে রবে দুনিয়াতে ,<br />একটু ভাবো মরন কালে তোমার সাথে কি যাবে ?<br />তাই আল্লাহকে ভয় করো ।",0,entertainment
চকমার কাহনি গুলা বেশি ভালো লাগছে।।।,0,entertainment
"ভাই এই ছবিটি অন্য চেলেনে আছে যদি পারেন তাহলে এমন কিছু আন কমান ছবি দিন যা অন্য কোন চেলেনে নাই কেন যে আপনারা দেখা ছবি গুলো বার বারদিতেছেন তা বুঝতে পারছি না এক ছবি যদি তিন, চার টি চেলেনে থাকে তাহলে কি লাভ বলেন ভাই",0,entertainment
নাটকে কথার সাউন্ডনাই কেন,0,entertainment
আসলেই রুচিসম্মত।,0,entertainment
"এটা কোন ধরনের নাটক? গল্প, অভিনয়, কিছুই হয়নি। এর থেকে বাজে নাটক এ বছরে আর দেখি নাই। আমার মনে হয়? নাটক কাকে বলে এ বিষয়ে সংশ্লিষ্ট প্রত্যেকের আরো ভালো করে জানা জরুরী।",0,entertainment
"শাবনূর তুলনা হয়না.এই যুগে সেরা নাইকা,আম প্রিয় নাইকা",0,entertainment
মনে হচ্ছে বলিউডের সং😯 এগিয়ে যাচ্ছে বাংলা গান♬ ♬,0,entertainment
মালা তুমি কার<br />মুভি টা দেন ভাইয়া,0,entertainment
আমার ফেভারেট বাপ্পা রাজ!,0,entertainment
তুদের মত কিছু মানুস আছে অব্দ্রাতা।। ছি জানাই তুদেরকে,0,entertainment
বাস্তব ছবি একটা দেখলা,0,entertainment
ফ্রেন্ডস প্লিজ আমার চ্যানেলটি করুন। আমি ও আপনার চ্যানেলটি সাথে সাথে সাবস্ক্রাইব করবো।,0,entertainment
যে একজন কে ছেড়ে আরেকজন কে ধরে সে ওকে ছেড়েই অন্য জন কে ধরবে স্বাভাবিক,0,entertainment
খুবই ভালো লাগছে মুভিটা,0,entertainment
ফকিন্নির বাচ্চা,0,entertainment
ইলিয়াস কাঞ্চন মানে সুপারহিট মুভি,0,entertainment
চলও আমরা সবাই এদেরকে ভালোবাসা দিয়ে ভালো পথে আনার চেষ্টা করি <br /><br />আমি একজনের দাইতও নিতে চাই,0,entertainment
"অনেক মিচ করি জসিম ভাই কে,",0,entertainment
ওই যন্ত্র তো হনুমানেরও আছে হুম্মম্মম্মম,0,entertainment
"ভাই যদি পারেন তাহলে রুবেলের,,,,<br />,,, জজ সাহেব,,, পলাতক আসামী,,, এই ছবি গুলো যে কোন একটা ছবি দিন ভাই",0,entertainment
পুরো ভিডিও কবে আসবো,0,entertainment
দুর মিয়া গাজীপুর কইয়া পচাইলেন 😂😂,0,entertainment
দারুন মুভি মানোয়ার ও শাকিব,0,entertainment
"এটা নাটক হলো, কি এটা",0,entertainment
নায়ক এমন কেন!!!,0,entertainment
এসব নায়কের ছবি কেউ দেখে না কি,0,entertainment
খুবই সুন্দর ছবি শাকিব খান মান্নাকে কত সম্মান করে কতা বলে আর স্নেহ করে শাকিব খান মান্না দুজন দুজনার ছবি অনেক সুন্দর,0,entertainment
নুসরাত ফারিয়ার এক্সপ্রেশন গুলো জোস😍😍,0,entertainment
আমিন খান পাওয়ার ফুল হিরো,0,entertainment
রুচি এতো খারাপ,0,entertainment
এই নাটক বুভা কে,0,entertainment
বু‌য়ে‌টে আবা‌সিক হ‌লের নাম রাখা হোক &quot;শ‌হিদ আবরার হল &quot; আর বু‌য়ে‌টের টং‌লেট গু‌লোর নাম রাখা হোক ওই কুত্তা‌রের না‌মে । এক মত হ‌লে নাইক ক‌রে জা‌বেন ।,0,entertainment
"অসাদরুন, মামুন ভাই,এবং মাসুম ভাই, নতুন গুলপ নতুন রুপে এরুকম একটি নাটক উপহার দেওয়ার জন্য",0,entertainment
এই কেমন নায়ক তুরো কারো কুনো রুচি নাই,0,entertainment
কমেন্ট পরে খিদে মিটে গেছে!! <br />কি আর মুবি দেখবো!!!,0,entertainment
"নাটক টা আগে একবার দেখছে, খুব সুন্দর একটি নাটক",0,entertainment
বস নাম্বার ওয়ান সাকিব খান কিং খান আমাদের জান,0,entertainment
এইডা কোন গান,0,entertainment
"একটা সময় হিমু হবার জন্য কতো সাধনা করেছি, ক্লাস সিক্সে পড়ার সময় হিমুর সাথে পরিচয়, তারপরই মাথার ভিতর চরিত্রটি ঢুকে যায়।",0,entertainment
ছবিটি দেখতে খুব সুন্দর,0,entertainment
কষ্ট লাগে মনে,0,entertainment
ওই মেয়েটাকে ধরে আমার কাছে পাঠিয়ে দাও আমি ওকে বুঝিয়ে বলব প্রথমে আমি ওকে হাতের কাছে পেলে মার তাম পুরো তিন মিনিট ধরে টস টস করে মারতাম তারপর ওর মাথায় ঠান্ডা পানি দিয়ে ওকে ঠাণ্ডা করে বুঝিয়ে বলতাম,0,entertainment
দেশের মানুষ মাসুম এত সুন্দর নাটক করে জানিনা,0,entertainment
এখনো সালমান শাহ আমার ফেবারিট,0,entertainment
আমি ছবিটি দেখে বাকরূদ্ধ হয়ে গেলাম,0,entertainment
অসধারণ খুব সুনদর ত্রইনাটকের অভিনয়গুলিআমার কাছে অনেক অনেক ভালো লেগেছে ত্রবং অভিনয়গুলিছিলো খুবই দারুন সুপার নাটক আর যারা ত্রইনাটকে অভিনয় করেছে তাদেরকে সবাইকে আমার পক্ষেথেকে অনেক অনেক ধনোবাদ,0,entertainment
রিয়াজ ভাইকে আজও চাই আর যত দিন বেঁচে আছি আমরা আমাদের সবার প্রাণের চেয়ে প্রিয় অভিনেতা রিয়াজ ভাইকে ভালোবেসে যাবে বলে আশা করা যায়,0,entertainment
এই সিনেমার মতো তোমার বাস্তব জীবন টা ৷তোমার দুই পৃথিবী অপু ও বুবলি কিন্তু দুই পৃথিবীর মাঝে ঘর করা <br />যায় না ৷পৃথিবী একটায় হয় আর <br />তোমার সেই পৃথিবী হল অপু ৷,0,entertainment
এরা কি জে আসলে এদের বিচারক রাখা হইছে,0,entertainment
"ইসলাম নিয়ে মজা করবে না। আর নয় ইসলাম নিয়ে মজা, না হলে জিব্বাহ টানে ছিরাবো। ইসলামের ঘোর শএু এসব জালিমেরা।তোমাদেরকে আগুনের ভিতরে পুড়ানো দরকার।সাবধান হও সাবধান হও",0,entertainment
আরে ভাই বিচারকগুলো কতগুলো ট্যালেন্টেড মাল্টিট্যালেন্টেড ফাটাফাটি এরা তো সবকিছুরই বিচার করতে পারে অনেক ধরনের অডিশন কিন্তু অনেক ধরনের পেশার বিচারকতো দরকারই নেই,0,entertainment
"আমার ওপ্রেম করতে ইচ্ছা হচ্ছে, এই ভিডিও টা দেখার পর। কিন্তু এই ধরনের প্রেম কোনো ভাবেই না। জীবনে যা একবারই আসবে। তারপর যে যত লোভ ই দেখাক না কেনো, প্রিয়তম জীবনে একবারই হবে। অসাধারন সৃষ্টি।তার মধ্যে আবার জসীমউদ্দীনের কবিতা। অপুর্ব...... ।",0,entertainment
মাহির সাথে আমিন খানেই বেষ্ট,0,entertainment
উল্টা ছুরি দিয়ে হাত কাটতে কেউ কি কখনো দেখেছেন যদি না দেখে থাকেন তাহলে দেখে নিন নিশো কিভাবে কাটে,0,entertainment
দেখছি ভালো লাগছে । 😍❤😊👌👏✌👍,0,entertainment
এতরাতে ভিডিও ছাড়ছেন এরপরেও মিনিটে হাজার ইম্নোসিয়া রোগীরা ভিডিও দেখে ফেলসে,0,entertainment
"মান্না ভাই বাংলার গর্ব, বাংলা সিনেমার আর্দশ। সিনেমা হলে এখন মানুষ যায় না, কারন আগের মতো ভাল ছবি হয় না। এখন কার সিনেমা গুলো জুকারদের মতো, অভিনয় গুলো জুকারদের মতো। মান্না ভাই আর আসবে না, এ আল্লাহপাক তাকে জান্নাত দান করুন।ভাল সিনেমা বানাতে পারলে মানুষ অব্যশইদেখবে, ইন্ডিয়ার নাটক দেখবেনা। আমরা আশা, করি আগের পরিচালকেরা এখনো ভাল হিরো নিয়ে ভাল সিনেমা বানাতে পারেন।",0,entertainment
সানাই কে পতিতালয় পাটিয়ে দাও,0,entertainment
"হিমু চরিত্রে রিয়াজকে আমার কাছে বেশি ভালো লাগলো, সে হুমায়ুন আহমেদের পরিচালনায় বহু নাটকের অভিজ্ঞতা সম্পন্ন।।",0,entertainment
ব্যবহারে বংশের পরিচয় কিন্তু সেটা হয়তো তাদের জানা নেই।,0,entertainment
হীরকে দেখের ইচ্ছাই মাট,0,entertainment
"গানটা সুন্দর,কিন্তু দৃশ্যটা অশ্লীল",0,entertainment
এমপি হলে চাইমচাদের পুষ্টির অভাব হবে না। নীচ তলায় ভাড়া দিয়ে উপর তলায় বড় করে। হা হা,0,entertainment
এমপি সাহেব ভিটামিনের গোডাউন পাইলেন,0,entertainment
তোমার সাথে যদি কোন দিন দেখা হয় তাহলে একটা শাড়ি উপহার দিবো তিসা রুবি ঢাকা,0,entertainment
ভালোবাসা এতো কষ্ট আগে জানলে প্রেম করতাম না একটা কথা সবসময় মনে রাখতে হবে যে ভাবিয়া করিও কাজ করিয়া ভাবিও না আজ আমি শুধু কষ্ট নিয়ে ‌বেচে আছি শুধু কষ্ট,0,entertainment
সাপের মুখে মধু,0,entertainment
"ছোটবেলায় বউজামাই খেলাতেও ভালো অভিনয় করছি আমি,, সালার পালতু সিনেমা",0,entertainment
অপু বিশ্বাস ও জিং য়ের ছবি চাই পিলিজ দয়াদেন,0,entertainment
"অথচ, স্রেফ মিডিয়া পরিচিতি পেতে এরা কাস্টিং কাউচ হয়!",0,entertainment
দেনমোহর নাটক থেকে টেনিং নিয়েছে৷,0,entertainment
আসলেই আমাদের দেশ অনেক সুন্দর,0,entertainment
আমি ত হাবিব ভাই পাগল তার গানে অন্য মায়া কাজ করে,0,entertainment
ভাই অনেক দিন পর রোস্টিং দেখে সেই আগের মজা পাইলাম। হ্যাভি দিছেন ভাই ভরে ভরে করে করে দিসেন,0,entertainment
"মিন্টু সম্রাট,গোয়েন্দা, বিক্রম, বির বিক্রমছবি গুলো আপলোড দিন",0,entertainment
একঘেয়ে জুটি। ধুস্!!!,0,entertainment
সব কটা ভুদাই ভদ্র মানুষ কোন দিন এই ভাবে কথা বলে নাকি। জাজ ফুডাইতে আইছে খ্যাতের থেকে উঠে আসছে এক একটা,0,entertainment
"কি বলিবো আমি সব কিছু অন্ধকার ভূমি,, <br />কি বলি বো কথা প্রানে শুধুই ব্যাথা... <br />আকাশ টা বড়ই কালো এই মনে নেই<br /> সুখের আলো <b>**</b>",0,entertainment
আমার প্রিয় মান্না ভাই,0,entertainment
"চিকন ও ধুতি খানী নাহি পারি বান্ধিতে, নাহি পারি বান্ধিতে কেশ",0,entertainment
আমি সৌদি আরব থাকি আমার একটা মেয়ে রেখে এসেছি এক বছর বয়সের ছবিটা সেশ পর্যন্ত দেখে মনটার মাযে অনেক কস্ট লাগছে,0,entertainment
হাবিব ওয়াহেদ ভাই রে আপনার কোপাল পুড়ছে,0,entertainment
বাকরুদ্ধ।অসাধারণ 👌👌 এতদিন মালালায়াম মুভি নিয়ে লাফালাফি করতাম। চোখে আঙুল দিয়ে আমার মনুষত্বকে আঘাত করেছে মুভিটি। What we have done for our motherland??,0,entertainment
আপু আপনার নিচ তালার ভাড়া কত,0,entertainment
"খুবই ভালো লাগলো রিয়াজের অভিনয়, গানগুলো চমৎকার বিশেষ করে .....তুমি আমার বুকেরই ভিতর আছো তুমি থাকবে তুমি সারাজীবন ভর&quot; এই গানটাবেশি লেগেছে ।",0,entertainment
এই ছবিতে যারা ভালো বলতাশো তারা সবাই জারজ সন্তান ।।,0,entertainment
সময়টাই নষট হল বাজে নাটক,0,entertainment
অামি তো ১৫৭ পর্ব পর্যন্ত দেখে ফেলেছি। সুতরাং এখন অার অপেক্ষায় থাকি না। অাপনারা মানুষের অনুভূতিগুলো নিয়ে খেলেন। &gt;:O,0,entertainment
"অনেক অনেক ভালো ছবি,,, পরিচালক কে ধন্যবাদ,,, 🏄🏂",0,entertainment
"আমার মতো জান্নাতে নাটক দেখতেঅপেক্ষা করো কে কে, কমেন্ট করে জানাও",0,entertainment
মজার ব্যাপার হলো এদের কেউ ই মাসুদ রানা হচ্ছেনা🤣🤣 ছবির পরিচালক রা হলিউড থেকে এসে সেদিন ইন্টারভিউ নিয়ে গেছে।। এদের একটাকেও দিয়ে হবে না এবিএম সুমন হচ্ছে মাসুদ রানা!,0,entertainment
রুবেল ছবি দেওয়া জন্য ধন্যবাদ,0,entertainment
জুতা দিয়ে পিটিয়ে চামড় তুলে নেয়া উচিৎ পরিচালকের,0,entertainment
সেই প্রেমে হইলাম আমি তোমার দিবানা,0,entertainment
অনিল কাপুর ও মাধুরী অভিনীত হিন্দি ছবি &quot; বেটা&quot; র হুবহু নকল।,0,entertainment
অনেক দিন পরছবিটা দেখতে মন ব্যাকুল হয়েছিলো। তাই আজ ছবিটা দেখলাম..... 😍😍😍,0,entertainment
কালো চশমা ছবিটা দিবেন,0,entertainment
আমার ভালোবাসা আফরান নিশো ও তানজিন তিশা খুবই চমৎকার একটি নাটক ও মন চমকানো আমার ভালোবাসা আফরান নিশো ও তানজিন তিশা এইরকম একটা নাটক উপস্থাপন করা জন্য পরিচালক ভাই আপনাকে অনেক অনেক ধন্যবাদ 👌💚👍 বাস্তব জীবনের ঘটনা গুলো ভেসে আসে নিশ্চয় আমার ভালোবাসা আফরান নিশো ও তানজিন তিশা খুবই চমৎকার অভিনয় করেছেন এবং সুন্দর হয়েছে নাটকটি ভালো লাগার মতো একটি নাটক উপহার পেলাম 👌💚👍 বাস্তব জীবনের স্বপ্ন গুলো উপলব্ধি করতে পারেন আপনারা আমাদের সম্মানিত সফল করতে পারেন আপনারা তার প্রমাণ রচনা ও পরিচালক ভাই আপনাকে অনেক অনেক শুভেচ্ছা ও অভিনন্দন জানাই আমার ভালোবাসা 👌💚👍 বর্তমান সমাজের পরিস্থিতি নিয়ন্ত্রণে আনতে আমার ভালোবাসা আফরান নিশো ও তানজিন তিশা এইরকম মানে এইধরনের চিন্তা ভাবনা নিয়ে আমার ভালোবাসা আরও ভালো রোমান্টিক গল্প গুলো দিয়ে সাজানো একটি নাটক উপহার দিবেন আশায় বাসা বাঁধি ভালো কিছু আশা করি আপনারা সবাই ভালো থাকবেন সবসময় এলোমেলো ভাবনাগুলো সুন্দর করে গুছিয়ে নিতে হবে তারপর বাংলাদেশের নাটক জগতের প্রেমিক আমি চাঁদপুরে কৃতি সন্তান রাজু আপনাদের অপরিচিত একজন ড্রাইভার আমি বাংলার নাটকের প্রেমিক 👌💚👍 আমি চাই আরও অনেক বাংলা নাটকের প্রেমিক হউক সার্থক হউক আমাদের বাংলাদেশের নাটক জগতের অভিনেতা ও অভিনেত্রী প্রতি আমার ভালোবাসা 👌💚👍 সবাইকে আমার সালাম জানাই আমার ভালোবাসা আফরান নিশো ও তানজিন তিশা এবং পরিচালক ভাই আপনাকে অনেক অনেক ধন্যবাদ 👌💚👍,0,entertainment
অনেক ছেলেই এভাবে নিজেদের জীবন নষ্ট করে দেয়। বিশেষ করে ছাত্র অবস্থায় নিজের মুল্যবান সময়টা,0,entertainment
আমি ইন্ডিয়া থেকে বলছি. এতো ভালো গান খুব কমে শুনেছি,0,entertainment
কে হবে মাসুদ পাগল,0,entertainment
আরবি ভাসাকে বাংগু করার অপরাধে পরিচারক এর ফাসি হবার দরকার,0,entertainment
আপনেরা ওদের কাছে কেমনে জান,0,entertainment
এই এিবুজ প্রেমের ছবি এখন হয় না।এসব ছবি এক কথায় অসাধারন। রিয়াজ সাবনুর পুর্নিমা এক কথায় অসাধারন।খুব মিস করি তিন জনকে।,0,entertainment
শাবনুর আপির সাথে দেখা করতে মনছা কিন্তু কি করে করবো,0,entertainment
হট শর্ট ফিল্ম মানেই শরির গরম! আহ ! কি যে ফিলিংস হচ্ছে আমার!,0,entertainment
ছোট বেলায় বিটিভি তে দেখেছিলাম।আর এখন আবার এই খানে দেখতেছি।,0,entertainment
ভালবাসার মানুষটাকে না পেলে দুঃখ করার কিছু নাই .ভালবাসার মানুষটাকে পেয়ে গেলে মানুষটি থাকে কিন্তু ভালবাসা থাকে না কিন্তু না পেলে মানুষটি থাকে না কিন্তু ভালবাসা থাকে অনেক আজীবন .আর ভালবাসার মূল্য তো অনেক বেশি .এ ভালবাসার স্বাদ অন্যরকম,0,entertainment
অন্যায়ের প্রতিবাত করতে গেলে<br />নিজেকে এমন ই হতে হবে,0,entertainment
"সেই ছোট ভেলা থেকে আমার প্রিয় নাইকা শাবনুর, এমনও সময় ছিল শাবনুরের ছবি চাড়া অন্ন কোনো নাইকার ছবি ভালই লাগত না,",0,entertainment
শাহনাজ খুশি কে চঞ্চলের মায়ের চরিত্রে ভালো মানাবে ।,0,entertainment
এটা কোনো নায়িকা হলো,0,entertainment
যাই বলেন ওকে ওর কোনো সমস্যা নেই,0,entertainment
আমার মতো কে কে জান্নাত দেখার অপেক্ষায় থাকো...তারাই হাত তুলুন.....?,0,entertainment
শাবনূরের উচিৎ হয় নাই এইরকম একটি বাজে ছবিতে অভিনয় করা।,0,entertainment
ধন্যবাদ দেবার ভাষা নেই ভাই,0,entertainment
খুউব খুউব শান্তি পাইলাম। আজ ঘুম ভাল হবে! থ্যাংকস ভাই!!,0,entertainment
শালা আগেরগুলো নতুন করে দিচ্ছিস।<br />আবার এর মধ্যেই তোদের নাম ঢুকিয়ে দিয়েছিস।,0,entertainment
আমার প্রিয় নায়ক,0,entertainment
রুবেলের রক্ত পিপাসা মুভিটা চাই।,0,entertainment
ভুল গানে ভুল নাছ।,0,entertainment
"মেহেদী এখন কয় থাকে, এতো নায়িকা আছে এখন তার",0,entertainment
"অনেক দিন পরে মহা নায়িকা শাবনুর এর ছবি, খুব ভাল লাগল",0,entertainment
অবশ্যই অসাধারণ হয়েছে,0,entertainment
নাটকটা আমার জীবনের সব থেকে বড় একটি উপহার,0,entertainment
ও আল্লাহ এই যুগের মেয়েরা কি এখনো এত বোকা আছে নাকি। একটু বাড়াবাড়ি হয়ে গেল না।,0,entertainment
তোদের মত মেয়েরা হচ্ছে বাংলাদেশের ভিআইপি ম মুখ খারাপ করতে চাইছিলাম না তারপরেও করতে হবে না,0,entertainment
কত সুন্দর সামাজিক ছবি৷ বেশি বেশি ৭০/৮০-র দশকের ছবি আপলোড দেওয়ার জন্য আপনাকে অনুরোধ করছি৷ ধন্যবাদ৷,0,entertainment
বর্তমানে এই ধরনের মুভির অনেক অভাব।বাংলা সিনেমা ভালো ছিলো আগে।,0,entertainment
আমি যদি বিচারক হইতাম এনাকে কখনো সুযোগ দিতাম না। আপনি নিজেকে কি ভাবছেন কে মুখ দেখাতে আসল না আসল তাতে আপনার কি কাউকে যোগ্য মনে না হলে তাকে নিবেন না। অপমান করার অধিকার আপনাকে কে দিয়েছে আপনার শিক্ষাগত যোগ্যতা নিয়ে আমার মনে প্রশ্ন থেকে গেল !! আবালের দল সব। কে বানায় এদের বিচারক,0,entertainment
রুবেল মানে নতুন কিছু রুবেল মানা সুপারহিট মুভি,0,entertainment
পজাকে কেমন লাকছে,0,entertainment
বরিশালের মানুষ বাসের ছাদে উঠেনা,0,entertainment
আসসালামু আলাইকুম ভাইয়া আর আপুরা। <br />তোমরা কেমন আছো সবাই।<br />তোমাদের নাটকটি কেমন লাগলো অবশ্যই জানাবে।,0,entertainment
পৃথিবীর সেরা একজন নায়ক,0,entertainment
দুই বাংলার নাইস ছবি,0,entertainment
তুই কি উপস্থাপনা করতে পারস আবাল,0,entertainment
খুবেই সুন্দৱ ছবি,0,entertainment
চঞ্চল চৌধুরী একটা মাল।।।,0,entertainment
আই লাইক ইউ,0,entertainment
দারুন হয়েছে সুপার ডুপার আর কাজী হায়াৎ বলে কথা ধন্যবাদ আর মারুফের আজ কালঅভিনয় অনেক ভালো হয়েছে,0,entertainment
মুস্তফা কামাল রাজ ছাড়া সব বিচারকের ভাব দেখে খারাপ লাগছে!,0,entertainment
হালার বিচারকেরাইতো উপযুক্ত না। তারা কি আবার বিচার করবে,0,entertainment
আমার প্রিয় পরিচালক কাজি হায়াত সাথে সাথে কাজি মারুফ ভাই অনেক অনেক সুন্দর হয়ে,0,entertainment
বাংলা নাটক এই জন্যে দেখতে মন চাই না। নাটক শেষ টা শেষ না করে শেষ,0,entertainment
সাকিব ভাইয়া হল আমাদের দুই বাংলার ভাইজান।,0,entertainment
"ধন্যবাদ মামুন ভাইকে, এমন একটা গল্প উপহার দেওয়ার জন্য।আর এই গল্পে আমাকে অভিনয় করার সোযোগ দেওয়ার জন্য।",0,entertainment
নাটক এ রকমি হওয়া উচিত,0,entertainment
আব্দুল জব্বার স্যার স্যালুট জানাই আপনাকে....,0,entertainment
"আসলে এটা ঠিক না মানুষের এরকম করা ।যখন মানুষ বুল সুদরাতে ছায় তখন তাকে তুমি সঠিক পথ দেখিয়ে দাও,আর তার কোন দুরবলতার সুযুক নিওনা।মানুষ ইছেচ করে কিন্তু সব কিছু করে না তার পেছনে কোন না কোন কারন থাকে?",0,entertainment
আবার কবে পরের গুলো পাবো?,0,entertainment
সাকিব ভাই আপনি অপু সাথে নতুন ছবি চাই,0,entertainment
আসলেই ওনেক সুন্দর বিটিভি তে দেখেসিলাম তাও কতো কষ্ট করে লুকিয়ে লুকিয়ে আসলেই ওইদিন গুলা ওনেক সুন্দর ছিলো 😂😂,0,entertainment
সবি ঠিক আছে কিন্তু ।স্বামী স্ত্রী র বয়স ঠিক নাই,0,entertainment
মেয়েটার হাসি খুব সুন্দর,0,entertainment
কয়েক মাস পুর্বে আপনার ক্যামেরা হারানোর কারনে অঝরে কেদেঁছিলেন আর এখন একটা ব্যাশা মেয়েকে নিয়ে এসে যুব সমাজকে নষ্ট করছেন এতে মানুষ কি শিখবে আপনি আশা করেন 👠👠👠👠👠👠,0,entertainment
যাক সংসদে দুধের গোডাউন যাচ্ছে সবাই দুধ খেয়ে মাথা ঠিক রাখবে,0,entertainment
বাংলাদেশি আইটেম গানের উন্নতি,0,entertainment
এগুলো কি অভিনয় কর ভালো কিছু কর,0,entertainment
"এই নাটক টাতে জানুকে অতিরিক্ত সুন্দর লাগে,,,,So cool....R Natok ta khobi HD,,thanks,,for uplod HD drama",0,entertainment
তৌকির আহম্মেদ কে ধন্যবাদ।,0,entertainment
"ভাই যদি পারেন তাহলে,<br /> বাংলার বধু ,বাপের টাকা ,গরীবে বউ, এই ছবি গুলো দেবেন আশা করি আমার অনুরুদ টুকু রাগবেন",0,entertainment
"ভাই আপনার কাছে কি অমিত হাসানের,আলী কেন গোলাম,এই ছবিটি আছে যদি থাকে তাহলে একটু জানাবেন কেমন ভাই",0,entertainment
কমেন্ট গুলো পড়ার পর নিজেকে নিজে মাইরা ফালাইতে ইচ্ছে করতেছে,0,entertainment
কি বাভে পাবো,0,entertainment
আপনাকে অসংখ্য ধন্যবাদ যে সাবনাম ফারিয়া আর ওই হনুমান কে নিয়ে এত সুন্দর একটা ভিডিও বানানোর জন্য যে মানুষকে সম্মান করতে জানেনা তাকে আল্লাহতালা পছন্দ করেন না মনডা চাইতেছে ভাই শুয়োরের বাচ্চার সামনে পাইলে কি যে করতাম আল্লাহ ভালো জানে,0,entertainment
"তখন কি ভালো গল্পের মুভি হতো,এখন এমন গল্পের ঘোচানো মুভি দেখাই যাইনা",0,entertainment
মুর্খ হালা আরবি না জানলে কি কাছ?,0,entertainment
এই ছবি টি ছোট বেলায় চট্টগ্রামের নেভি হলে একবার দেখে ছিলাম,0,entertainment
ভাই আমার নাম টাই কলঙ্ক করে দিলো সালায়...😭😭😭😭,0,entertainment
তোমার দেহ ও মনকে ভালোবাসতে তোমার স্বামী আছে 👫,0,entertainment
বাহ - খুব সুন্দর ভিডিও!,0,entertainment
"আমার দেখা বাংলা সেরা ছবি😍👌<br />দেন, আমার শট নামও দীপু😊",0,entertainment
সত্যি খুব ভাল লাগল ছবি,0,entertainment
বাকি নাটকের অপেক্ষায় রইলাম,0,entertainment
আপনাদের ভালোবাসা পেয়ে সত্যিই আমরা খুব আনন্দিত। সবগুলো নাটকের মত এই নাটকটিতেও আপনাদের ভালোবাসা আশা করছি। ভালো থাকুন সুস্হ থাকুন আর পাশেই থাকুন। ভলোবাসা অবিরাম❤️<br /> Love u my friends,0,entertainment
লাইলী মজনু প্রেম কাহিনীকেউ হার মানাবে এই মুভি...লেখককে অনেক ধন্যবাদ এরুপ কাহিনী তৈরি করার জন্য....,0,entertainment
ভাই ভার্জিন মানে ওই বুড়া দাদা মনে হয় জানে না🤣🤣🤣,0,entertainment
ফাইন মুভি হয়েছে,0,entertainment
চোখে জল এসেগেল ভাই,0,entertainment
শাবনুর আপুকে রিয়াজ ভাইয়ের সাথে দেখতে চাই নতুন ছবিতে,0,entertainment
অনেক বোঝার আছে,0,entertainment
হাইরে সালার ছবি এক লাফে নদী পাড়,0,entertainment
গরিবের বাড়িতে চাবুক থাকে এই প্রথম দেখলাম...নাকি চম্পাকে পেটানোর জন্যই চাবুকটা রাখা হয়েছে?,0,entertainment
নায়ক উজ্জলের ছবি আপলোড দিবেন প্লিজ,0,entertainment
ভাই যদি পারেন তাহলে ঈদের দিন একটা আন কমান ছবি দিন যা অন্য কোন চেলেনে নাই বুজেছেন ভাই আপনার কাছে অনুরোধ,0,entertainment
আলেকজান্ডার আর রুবেলের ছবি অনেক ফাইটিং হিরো,0,entertainment
সাকিব তো একটা ছাগল ওর গান সোনে কেউ,0,entertainment
নাটকটার কোন মানে বুঝলাম না,0,entertainment
আচ্চা নাটকটা দেখতে কেমন?,0,entertainment
স্বামী-স্ত্রী দুজনই ভালো একজন মানুষ,0,entertainment
কমেন্ট টা রেখে গেলাম😍😍,0,entertainment
দাদা দারুণ হয়েছে,0,entertainment
যেকোনো নাটকেই হোক না কেন তার কথাগুলো খুবই মজার খুবই ভালো লাগে,0,entertainment
ভাই প্লিজ আপনাদের কাছে অনুরোধ করতেছি,0,entertainment
তোমাকে দেখে আমার ছোটো বেলার সেই গল্প টা মনে পড়ে গেল। এক লেজ কাটা শেয়াল গল্প। এটা তো তুমি জানো অবস্যই তাই না। তুমি হচ্ছ সেই লেজ কাটা শেয়াল।,0,entertainment
নাটকে মিল না হলে বেশি ভালো লাগেনা।রাজু মালয়েশিয়া থেকে,0,entertainment
অনেক কষ্ট লাগলো।ভালো হয়েছে ভাই।,0,entertainment
ভাল না ভেজাল আছে,0,entertainment
শয়তানের ফুরি,0,entertainment
"আমার ফেবারিট মুভি যেতো ভার দেখি তো বার চোখের ঝল নেমে আসে।। বাংলাদেশে অনেক নায়ক আসবে যাবে আমার মনে হয় সালমান শাহ মতন আর নায়ক আসবে না,, 😂😂😂 সিলেট আমার অহংকার",0,entertainment
খুব ভাল একটা নাটক,0,entertainment
"ধন্যবাদ, তবে এতো দেরি করা ঠিক হয়নি।",0,entertainment
বুকস নাড়াচাড়া 😒😒 হোস্টও মজা নেয়।,0,entertainment
দেখতে হিজরার মতো এ কিভাবে নায়কা হয় আসলেয় তার কি কোন মুভি আছে 🐶🐶,0,entertainment
সবার কপালে যদি এই রকম বউ হয় তাহলে ভালো হতো আমার ভালো লাগলো,0,entertainment
"সাকিব তার যোগ্যতা দিয়ে কিং খান।মান্না সুপার,",0,entertainment
সালমান শাহ্ নায়ক ছিল না সে ছিল মহানায়ক যা আমাদের মাজে আর কোনো তিন হয়ত আসবে না।,0,entertainment
মোশারফ মানে আলাদা বিনোদন,0,entertainment
মমোর ভিডিও দেখে আামাদের দারায় না,0,entertainment
সজিল ও তিশা সবার অভিনয় খুব ভালো হয়াছে,0,entertainment
আমার শাকিব খান জান জান,0,entertainment
"নাব্বার,ওয়ান,,,রিয়াজ,,,,",0,entertainment
আজাইরা বাংলাদেশের নাটক বাংলাদেশের জন্যই লক করা। VPN দিয়ে দেখতে হচ্ছে।,0,entertainment
ফালতু একতার নিউজ দেন কেন একটা ফালতু নাইকা তাই ভালো নিউজ দিবেন অর মতো একটা ফালতুর নিউজ দিবেন না আজাইরা,0,entertainment
"আমি ভারতিয়বাঙ্গালী , আমার কাছে অসাধরণ লাগলো এই সুন্দর ছবি টি",0,entertainment
"ছবিটা জতবার দেখলাম ততো বারেই দেখতে ইচ্ছা করে,,,",0,entertainment
এই রখম মোমি করার বোল,0,entertainment
আমি একজন প্রবাসী পারিবারিক কারণে মনটা অনেক খারাপ ছিল কিন্তু এই নাটক দেখার পরে মনটা এত আনন্দ হল যা ভাষায় প্রকাশ করার মত নয় ধন্যবাদ জানাই সকল অভিনেতাদের কে এবং ধন্যবাদ জানাই সালাউদ্দিন লাভলু কে ভাই,0,entertainment
"নাইকা,শখকে,কেনো,আমার,এতো,<br />ভালো,লাগেছে,,ওর,ফেজটা,যানো,ঠিক<br />আমার,ভালো,বাসার,মতো",0,entertainment
পরিচালক এর মাথা খারাপ। বাবা মেয়ে হইলো।,0,entertainment
কোন তামিল/তেলেগু মুভির কপি? 🙄,0,entertainment
"অনেক মুড নিয়ে মোসারফের নাটকটা দেখতে লাগছিলাম,, যখনই ওর বউকে দেখলাম তখন আমার নাটক দেখার মুডটাই নস্ট হয়ে গেলো",0,entertainment
"ভাই আপনাদে কাছে অনুরুদ যদি পারেন তাহলে রুবেলের ,<br />,জজ সাহেব, পলাতক আসামী, নেশা, এই ছবি গুলো দেবেন ভাই আপনাদে কাছে অনুরুদ",0,entertainment
নল,0,entertainment
"কাজী হায়াতের ছবি মানে হিট। সেই দাঙ্গা, এাস, ঝড়, আম্মাজান, কষ্ট, ইতিহাস, অন্ধকার আরো অনেক........….",0,entertainment
একটা মেয়ের জন্য সব মেয়েদের দোষ।,0,entertainment
মুভির কপি মনে হইতেছে 😐,0,entertainment
ওরা মানুষ নামের কলংক যারা মানুষ কে সম্মান দেতে জানে না তারা মানুষ না ওনাদের মত কিছু মানুষের জন্য আজ আমাদের শিল্প সংস্কৃতি ধংস হয়ে যাচ্ছে তারা চাই নতুন কোন মুখ যাতে অভিনয় করতে না আসে সবাই এদের কে দিগকার জানায় ও ওদের মত অভিনেতাদের অভিনয় না দেখার অনুরোধ করা হলে।,0,entertainment
সানাই কে বলতেছি ও একটা ম ইসলাম ধর্ম কে অসম্মান করছে ওকে এই দেশ থেকে বিদায় করা দেওয়া উচিত,0,entertainment
যতবার দেখি ততই ভালো লাগে।,0,entertainment
ভাই আমারে কেও ধর খালার খাইলাম আমি ধরল হেগুরে আর কী কুমু সব ত কমেন্ডে বলই সবাই,0,entertainment
জসিম এর ছবি আপলোড় দেন,0,entertainment
এদের জন্য দুনিয়াটাই সবকিছু আখিরাতে কি জানি কি হবে ❕,0,entertainment
বালের ছিনেমা,0,entertainment
আরবি ভাষা হয় নাই,0,entertainment
ভুল গানে ভুল নাচ,0,entertainment
বাবু ভাইয়ের মত প্রতিভাবান কখন ও দেখিনাই,0,entertainment
"আসলো অসাদারন হয়েছে,,,",0,entertainment
মামুন ভাই আপনাকে হিরোর পার্ট নিলে আরও ভাল হতো । কিন্তু আপনাকে এই পার্টে আপনার ভক্ত হয়ে আমি আমার মানতে কষ্ট হচ্ছে।,0,entertainment
নিসো কি ভাবে পারে এমন ভালো অভিনয় করতে,0,entertainment
অনুর্পম ভিডিও প্রিন্ট ভালো হয় এদের মত প্রিন্ট করা যায় না বাংলাদেশর সব চেয়ে ভালো প্রিন্ট করে অনুর্পম কম্পানি আপনারা ও ভালো প্রিন্ট করেন বর্স??,0,entertainment
ভালবাসা অনেক কস্ট আজ ও নিজের ভালবাসা কে ভুলতে পারি নি,0,entertainment
কোটি টাকা খরচ করেও মুভি বানালেও মাসুদ রানা মুভি টা দেখবোনা আর বাংলা মুভি খুলা একদমই ভালো লাগেনা ভাইই ক্ষেত মারকা মুভি,0,entertainment
জীবনে কোন মুভি মনোযোগ দিয়া দেখি নাই এই কাহিনীটা আমি অনেক মনোযোগ সহকারে দেখেছি এবং আমার ভেতর থেকেও জোরে জোরে কান্না,0,entertainment
ভালোবাসার গল্পটা সহজ হয়ে গেলো।,0,entertainment
ছেলেটা হালা আবাল ইয়াবা খোর,0,entertainment
আমি অনেক কষ্ট পেলাম এই নাটক দেখে,0,entertainment
একশেনে যাওয়া উচিত,0,entertainment
"চম্পা, ওয়ান এন্ড ওনলি",0,entertainment
এডিটিং খুব ভালো হইছে,0,entertainment
নাম কি মুবির,0,entertainment
বাংলার বুকে এরকম ছবি কি আর হবে,0,entertainment
রুবেল সোহেল রানা এদের দুই ভাইয়ের মিলনমেলা আবারও দেখতে চাই।,0,entertainment
এতদিন পরে মুভিটার ট্রেইলার!!!!,0,entertainment
"কে বলছে ছেলেটারে অভিনয় করতে, অন্য কাওকে দিয়ে অভিনয় করালে অনেক ভালো হতো আর সবার প্রশংসাও পেতো",0,entertainment
বাংলা মুভির পরিচালকরা জুকার।,0,entertainment
"ওরা কারা যারা আনলাইক দিছে? হুশিয়ার হও সময় থাকতে এরকম দেশপ্রেম অনুভূতি না থাকাও দেশদ্রোহিতার সামিল, আর দেশপ্রেমও ঈমানের অঙ্গ, আর সেদিক থেকে বিবেচনা করলেও আপনারা মুনাফেক। আমার কথায় যদিও কোন হতভাগার দ্বিমত থাকে তাহলে আশা করব শালীন ভাষায় রিপ্লাই দিবেন, অশালীন ভাষায় লিখে নিজের বংশের পবিত্রতা নষ্ট করে অন্তত নিজের রক্তকে অপমান করবেন না, তাহলে আপনার দেহটাও মানুষ নামটা হারিয়ে ফেলবে। ধন্যবাদ।",0,entertainment
মুভিটা দেখার খুব ইচ্ছে ছিলো কারন নায়িকা শাবনূর আর শাবনূর মানেই অসাধারণ কিছু খুব ভালো লাগলো,0,entertainment
সুপার মুভি বাংলাদেশের এ্যাকশান কিং রুবেল আমার প্রিয় নায়ক তার ফাইটিং অসাধারণ,0,entertainment
"নাটকটা দেখলাম অসাধারণ,",0,entertainment
অসাধারণ খুবই সুন্দর সবার অভিনয় খুব ভালো লাগলো,0,entertainment
মাসুদ রানার ছেলে মেয়ে কয়টা জানতে চাইলেন মাসুদ রানা কয় বার সহবাস করতেন এটা মমো ডাইনি জানতে চাইলেন না কেনো,0,entertainment
অসাধারণ ও দারুণ হয়েছে,0,entertainment
একদম সঠিক কথা। এজন্য বাংলা মুভির বে,0,entertainment
মনের মত একটা সেরা নাটক🤗🤗🤗,0,entertainment
প্রবাস থেকে কে কে দেখছো সারা দেও,0,entertainment
এর সাথে হিরো আলমকে বিয়ে দেওয়া উচিৎ,0,entertainment
সেরা অভিনেতা অবশ্যই মোশারফ করিম বাংলাদেশ,0,entertainment
ভাই জোশ কয়টা পয়েন্ট ধরছেন 😂😂😂,0,entertainment
আমার জিবনে সবচেয়ে বেশি বার দেখা রুস্তম সিনেমা,0,entertainment
জানো হঠাৎ করেই আমার মনে হয়<br />আমিকিছু হারিয়ে ফেলেছি<br />আমার অসম্ভব কিছু প্রিয়😢😢😢,0,entertainment
আগের বাংলা ছবি ছিল ছবি <br />এখন করে যাত্র,0,entertainment
গোঁফ আর ঢাকাইয়া ভাষাতেই অনন্তকে ভালো লাগছে,0,entertainment
কল্পনার হিমুর সাথে আমি কোন কিছুই মিলাতে পারিনা। এটা একদম আলাদা স্বত্তা। এরকম কোন নাটক দেখলে খারাপ লাগে। 1 টা মিনিট যাওয়া মানে মনে হয় আমি আমার চিন্তাজগতের হিমুকে হারিয়ে ফেলছি।,0,entertainment
তাদের আবার সম্পর্ক সম্পর্কের মানে বুজে ওরা।,0,entertainment
মোশারফ করিম ছাড়া নাটক দেখতে ভাল লাগেনা।,0,entertainment
অনেককষ্টেরছবিএটা এরকম ছবি মনে হয়জীবনে আর হবেনাআর বর্তমানতহবেইনা,0,entertainment
"গ্রাম বাংলার নাটক দেখতে অনেক ভালবাসি,,,,,,এবং গ্রামের কিছু বাস্তব ঘটনা তুলে ধরার জন্য ধন্যবাদ,,,,,,আশা করি আরও ভাল ভাল নাটক দেখতে পারবো,,,,,,,,",0,entertainment
খুব ভালো ভিডিও টাই লাগতেছে,0,entertainment
এটা তো আমার বউ এর থেকে বড় 😑,0,entertainment
সত্যিকারের ভালবাসা কখনো<br />হারিয়ে যায় না?<br />হয়তো বা মানুষটা কিছুই সময়ের জন্য<br /> তার জীবন থেকে হারিয়ে যায়।।<br />আর সেই সৃতি গুলা দুইজনকে কষ্ট হয়ে ভাসে জীবন নামের রেল লাইন টা,0,entertainment
এই মেয়েকে আমি যদি পেতাম 😡😡😡 তাহলে টস টস করে কয়টা তাপপর মারতাম বেয়াদব মেয়ে আমার মনে হয় তার পরিবার তার মতোই😡😡😡😩😨,0,entertainment
সব গুলো বিচারককে জুতা দিয়ে মারা উচিত মানুষকে ছোট করছে এতটা বাজে বিচারক নিজেরা কিছু একটিং জানে না আসছে বিচার মারাতে,0,entertainment
এরকম মুভিই আমাদের দরকার পুরো মুদরাই জোস বিষেশ করে রমজান কাকার অভিনয় টা অতুলনিয় 👌👌👌,0,entertainment
বিচারকদের কাছে পাইলে জুতা দিয়া পিডাইতাম বাবা মা ভদ্রতা শিখায়নি😠,0,entertainment
এদেরকে কে এখানে বসিয়েছে। এমন বিচারকে লাথি মেরে এখান থেকে উঠিয়ে দেওয়া উচিৎ,0,entertainment
আদালতেরজানের বাজী রেখে বিষপান অসাধারণ অভিনয়।,0,entertainment
গরীব ছাড়া ধনী চলতে পারবে না।,0,entertainment
আলমগীর বুঝেছে জসীম কি জিনিস,0,entertainment
ছবিটা অনেক ভাল লেগেছে অনেক আগে দেখেছিলাম আবার দেখলাম ধন্যবাদ আপনাকে,0,entertainment
তানজিন এর সাথে মশা কেন ?মশা এখন আর চলে না ?,0,entertainment
ভুলেও কোনো বাংলাদেশ এর রিয়েলিটি শো এ জাইয়েন না ভাই মান সম্মান শেষ।,0,entertainment
অনেক দিন পর দেখলাম চবিটা ধন্যবাদ,0,entertainment
"ভাই আপনার কাছে কি ইলিয়াস কানছনের,,, অন্ধ বধু,,, শান্তি চাই,,, শান্তির বদলে শান্তি,,, পাপের শান্তি,,, নৈয় যুদ্ধ,, সাধীন,,দংশন,, লটারি,,, দিনমজুর,,, টপ মাস্তান,,, সংসারের সুখ দুঃখ,, সুন্দরী মিস বাংলাদেশ,,, আজকের শয়তান,,, মাটির কসম,,, মানে না মানা,,,বিচার পতি,,,যদি এই ছবি গুলো থাকে তাহলে দয়া করে যে কোন একটা ছবি দেবেন ভাই আপনার কাছে অনুরোধ আশা করি আমার অনুরোধ টুকু রাখবেন ভাই",0,entertainment
কিছু বলার ভাষা খুজে পাচ্ছি না।,0,entertainment
"আমাদেরমাজে তেকে এমন একটামানুষহারিয়ে গেলও তার কোনো বিচার নাই,,,,একন ও চবি দেকলে চোখ দিয়ে জল আসে,,,,,,",0,entertainment
মজার টিভি এখন গাঁজার টিভি হয়ে গেছে 😆😆😆,0,entertainment
ভাই রুবেলের দিন মজুর ছবি আপলোড করেন,0,entertainment
যতোসব বাজে গল্প,0,entertainment
সেরা নায়ক রিয়াজ,0,entertainment
কিয়মতের অালামত,0,entertainment
আমি খুব খুব দুঃখীত এই জন্য যে আমি কুষ্টিয়ার ছেলে হয়েও এই ছবিটা এতোদিন দেখিনি। কুমারখালি কুষ্টিয়ার সব প্রতিভাদের এক ফ্রেমে বাঁধানো। <br />অসাধারণ পরিচালনা 👏👏👏👏,0,entertainment
অনেকদিন আগে উপন্যাস টা পড়েসিনেমা দেখার খুবই ইচ্ছেহইছিল আজ তা পূর্ণ হলো। <br />সত্যিই অসাধারন একটা সিনেমা। চোখের পানি আটকে রাখতে পারলাম না।,0,entertainment
তোমার মত আদর করে না এই গানটা খুবই ভালো,0,entertainment
শানাই তুমি কেমন আচ।,0,entertainment
একটা বালের ছবিভালো না,0,entertainment
অসাধারন হয়ছে,0,entertainment
শরীরের উত্তাপ ভাগাভাগীর ইচ্ছা অপূর্ণই থেকে গেল.....,0,entertainment
এইগানে যারা ডিসলাইক দেয় তারা গান বুঝে না।,0,entertainment
"একটা সিরিয়াল দেখার জন্য এত অপেক্ষা করাইয়া রাখা ভালো নাহ,,<br />নিয়মিত এবং দারাবাহিক ভাবে পর্ব গুলো দাওয়ার অনুরোধ রইলো,,",0,entertainment
"ছবিটা খুভ ভাল লাকছে,",0,entertainment
গুড শর্ট বস,0,entertainment
"আমার শুধু আফসোস বাপ্পারাজ এর জন্য, আহা বেচারা, সারা ছবিতে নায়িকার প্রেমে ছ্যাঁকা খাইয়া কান্দে আর শেষ দৃশ্যে ভিলেন এর গুলি খাইয়া মরে। পৃথিবীতে ছ্যাঁকা খাওয়ার যদি কোন পুরস্কার থাকতো আমি নিশ্চিত (বাপ্পারাজ) অস্কার বিজয়ীছ্যাঁকা অভিনেতা হতেন। 😁😁😀😀😂😂😃😃😆😆",0,entertainment
বাকিগুলো আপলোড দিন,0,entertainment
রিলিজ এর তারিখ দিবেন,0,entertainment
নবিহুসেন ভাই দারুন অভিনয় করেছে।,0,entertainment
তোদের মাথা গুলাই ফাটাবো বেয়াদদ্দব! 😠😠😠,0,entertainment
অনেক ভাল লাগলো মান্না ভাইয়ের অভিনয় অামার ভাল লাগে,0,entertainment
নাটক দেখে কি লাভ যদি এই টেকনিকাল সমস্যা র দিকে কর্তৃপক্ষেরনজর না থাকে !,0,entertainment
দুস্ত ভালো হইছে কাজটা,0,entertainment
খুব ভালো লগলো এটাতো কোনো পরকিরিয়ানয় একজন অসহায় মেয়েকে ভালো বেসে তার পাসেদারালো এ সমাজে কিছু দুষকৃতি লোক আছে যারা মানুষের দুরবলতার সুযগ খুজেতাই ছেলেটার ভালো বাসাটা কে মনদ লোকেরা খারাপ দিকটা দেখছে তার ভালো দিকটা দেখনাই,0,entertainment
দিলদার এর অভিনয় খুব সুন্দর হয়েছে,0,entertainment
আমার প্রিয় মুভি,0,entertainment
বাংলাদেশে কি নায়েক এর অভাব পরছে!?😂😂😂,0,entertainment
নাটক টা অনেক ভালো লাগছে খুবি মজার ছিলো,0,entertainment
"ধন্যবাদ আপনাকে ভাই মুভিটা আপলোড দেওয়ার জন্য, মাটির কোলে ছবিটা দেবেন প্লিজ ।",0,entertainment
বড়দের সামনে গিয়ে সালাম না দিয়ে কথা বলা।,0,entertainment
এভাবেই তৈরি হয় নয়ন ভন্ড,0,entertainment
বাই আর বোন এই গান শুনতে মনচুয়ে জায়,0,entertainment
আমি দোয়া করি মান্নাজান্নাতবাসি হোক,0,entertainment
হিমুর আর কোনো সিরিজ কি আসবে??,0,entertainment
সালি গো গোড়া দিয়া মারতে হবে,0,entertainment
এবার নিয়ে তিন বার দেখা হল,0,entertainment
ভাই আপনি তো মুসলিম নামাজ পড়েন???,0,entertainment
নাটকটা খুব ভাল লাগল।,0,entertainment
ভাই রে ভাই একটু তাড়াতাড়ি পর্ব গুলো দেন 😑,0,entertainment
মিষ্টি হাসির তুলনা হয় না ।,0,entertainment
"এর থেকে জদি কাবিলা কে নায়ক বানাইতো তাও ভালো হতো ,,",0,entertainment
মুভি টা খুব সুন্দর?? 👍👍👍💜💜👌👌👌👌👏👏👏,0,entertainment
"বস আপনার কাছে আমার একটা অনুরোধ। সোনালী রুপালি। নামে একটা চ্যনেল আছে ওই চ্যনেল এর কাজল রিপন ভাই এর কাছে। সুন্দরী মিস বাংলাদেশ, একটা ছবি আছে ওই চ্যনেল থেকেছবিটা আপলোড দিলে খুসি হতাম",0,entertainment
ভাই আপনি ফারিয়া মামা রে ভাই কইলেন কেন 🙄 কথা কি ক্লিয়ার আছে না ভেজাল আছে 🙄🙄,0,entertainment
এই মেয়েকে কে এই জাগাই আনছে!!,0,entertainment
আজ থেকে ১৪ মাস আগে দেখেছি ꫰কাতারে এসে দেখেছি꫰,0,entertainment
সত্যি ছবিটি দেখে চোখে পানি চলে এলো।অসাধারণ মভি।,0,entertainment
নাটকের আগা মাথা কিছুই বুঝতে পারিনি ।,0,entertainment
এমন সুন্দর জায়গা জেলায়,0,entertainment
দারুন ভালো,0,entertainment
আমার কাছে অনেক ভাল লাকছে ছবি টা এরকম ছবি আর,0,entertainment
"আমি এমনিতে সকিব এর মুভি দেখিনা,এ মুভিটা ওনেক ভালো লাগছে",0,entertainment
কোন ফাগুনের ফুলগো তুমি,0,entertainment
ঋদয়ের মানুষ এরা !,0,entertainment
তোমার হাত পাখার বাতাসে।ছবিটা সুন্দর। বাবার জন্য যুদ্ধ।,0,entertainment
গানের মইধ্যে উহ করাডা এতোটাই বিরক্ত লাগছে বুজাইতে পারুম না।,0,entertainment
আরাবি নিয়ে এত কটাক্ষ করা উচিত নয়,0,entertainment
ভাল বাপের খারাপ পোলা।।,0,entertainment
আমি যখন এই মভিটা দেখি তখন আমার পাশে আমার স্বামি ছিলো আর আজকে যখন দেখলাম তখন সে আমার থিকা অনেক দুরে কারন তার সাথে আমার অনের দুরুত,0,entertainment
শাবনুর আপুর অভিনয় দেখতে কার কার ভালো লাগে 💜💜💜💜💜💜🙌🙌🙌🙌 like 👍👍👍,0,entertainment
ছবির টা থেকে গানগুলোঅনেকভালো ঈইলাই কেট...........,0,entertainment
ছবিটা দেখে আফসোস হয় খুব আমাদের সমাজের ঘরে ঘরে যদি বুলবুল আহমেদ এর মতোন বাবা থাকতো তবে আমাদের বাংলার ঘরে ঘরে আজ অনেক প্রতিভাবান সন্তানের লুকানো প্রতিভা ঘরের কোণে ডুকরে না কেঁদে বাইরের জগতে বেরিয়ে বিশ্বের বুকে মাথা উচু করে দাড়াতে পারতো দেশের সম্মান উচ্চশিখরে পৌছে দিতে পারতো। বাবা মায়ের সামান্য সহযোগীতার অভাবে আজ অনেক সন্তান বিপথে এগুচ্ছে যা খুবই দুঃখের বিষয়।,0,entertainment
রিয়াজ ভাই এর মুভি চায়,0,entertainment
ওদের কথা বাদ দিয়ে আপনার কথা বলেন বাহ বাহ বাহ এর মানে কি,0,entertainment
বাবার আদর মায়ের স্নেহ ভালবাসার অতৃপ্ততা আর বন্ধুত্বের আবেগ ঘন ভালবাসা স্পেশালি গল্পের কেন্দ্রীয় চরিত্র দীপু তারিক নান্টু বাবুলতাদের বন্ধুত্বের বন্ধনের দৃষ্টান্তবিরল। ছবিটি দেখে চোখের কোনে কখন যে জল এসে গেলবুঝতে পারি নি।সবচেয়ে বেশি খারাপ লেগেছিল দীপুর সাথে তার মায়ের সাক্ষাতকার এবং তারিক তার ফ্যামেলির কথাগুলো যখন দীপুর সাথে শেয়ার করছিল।,0,entertainment
সত্যিই অসাধারণ কিন্তু দুজনের পুরোপুরি মিল দিলে একটু ভালো হত,0,entertainment
মাই টিভি বাংলায় দেখলাম তৌহিদ নিজেকে বড় করে আত্নপ্রচার করেছে সে হিরো আলমকে অপমান করেছে অনেকে তাকে(তৌহিদ কে) কঠিন কথা বলেছে কে কে সেটা দেখেছেন।,0,entertainment
আম্মাজান ছবি দেন<br />সাথী ছবি দেন<br />কুলি ছবি দোকানে দেখলাম আজকে বলাই লাগল,0,entertainment
সেই ছটো বেলা থেকে পুরামন ছবির গান সুনছি আর আজ দেকলাম পুরামন ছবিটা.......onek sonsse ai sobir khta......?,0,entertainment
প্রবাসী ভাইয়ারা সাথে থাকুন,0,entertainment
"খুব সুন্দর একটা নাটক।<br />গল্পটা অসাধারণ, মন ছুয়ে গেছে। গ্রাম্য চরিত্রে অপূর্ব ভাইকে আরো বেশি বেশি দেখতে চাই।",0,entertainment
হায় আল্লাহ বিচারকের যা অবস্থা। বাংলাদেশে বিচারকের জায়গায় কেউ গেলে নিজেকে ভাবা শুরু করে!,0,entertainment
ভাইয়া এসোবের বিচার ওপর আল্লাহু করবে আমরা বলে গোনার ভাগি হতে চাই না । কি বলেন সবাই আসেন আমরা সবাই আল্লাহ্কে সরন করি কেমন????,0,entertainment
ভালো হয়নি,0,entertainment
"পোস্টার যে করছে সে একটা আবাল,মেন নায়ক বাপ্পারাজ তার ছবি নাই।",0,entertainment
একজন নারী পা থেকে মাথা পর্যন্ত প্রত্যেক অঙ্গ একটা পুরুষের জন্য ভালোবাসা আর যদি হয় পা থেকে মাথা পর্যন্ত প্রত্যেক অঙ্গ সব পুরুষের ভালোবাসা পেতে চায় তাহলে তাকে কি বলে বাজারের মাঘি,0,entertainment
সরকারের বাপ তাহলে তুই নাটক করো কেন,0,entertainment
দারুন হইছে,0,entertainment
দুইজন আমার খুব ভালো লাগে,0,entertainment
মনে পরে সেই দুরন্ত শৈশব।।,0,entertainment
সাকিবের কষ্ট দেখে চোখের পানি দরে রাখ তে পারলামনা নাইস,0,entertainment
"চমৎকার , অসাধারন",0,entertainment
অসাধারণ এ্যাকশন মুভি রুবেল এন্ড সিনা জুটি,0,entertainment
ডিসলাইক দিয়েছে কারা<br />জাতি জানতে চায়,0,entertainment
চঞ্চল দা অসাধরন।,0,entertainment
ধন্যবাদ মান্নার সিনামা আপলোড দেয়ার জন্য..,0,entertainment
"এক কথায় অসাধারণ,,,,✌♥<br />অনেকেই উপকৃৎ হবে নাটক টি দেখে,,,<br />অসখ্যা ধন্যবাদ পরিচালক কে, এতো সুন্দর একটি নাটক উপহার/দেখানোর জন্য,,,,♥🌹<br />এই প্রথম ইউটিউব এ কমেন্ড করলাম,মূগ্ধ হয়ে গেলাম,,,",0,entertainment
ভাইয়া অনেক জোশ,0,entertainment
প্রশ্নগুলার কোন রং ছিলো নাহ👌👌,0,entertainment
"ধন্যবাদ, পরবর্তি পর্ব চাই",0,entertainment
মন ভাল করার মত একটা নাটক,0,entertainment
আমিতো এই টা তিনবার দেখেছি,0,entertainment
ভালো করেই হোগা মারা দিলেন হাহাহা,0,entertainment
বস আসলে তুমি সব পারো,0,entertainment
ডিজিটাল মুভি দেখতে কনো ফিলিংস লাগেনা।আগের মুভি গুুলোই ভালো ছিলো,0,entertainment
এ নায়টির নাম কি? সেই লাগে,0,entertainment
"শেষের গানটা অনেকসুন্দর ভালো লাগার মত, জিনি লিখেছেন হাজার সালাম",0,entertainment
এসব মুভির প্রচারণা হয়না কেন? এত ভালো এত ভালো।,0,entertainment
শাকিব খান হলে খুব সুপার হিট হত।,0,entertainment
পুরাই সেই...এটা দেখি ★জলসা,0,entertainment
আচা নাকিতা হাসতে হাতে মুতে দরিলাইচে বে,0,entertainment
মিডিয়ার মানুষ গুলা এমন কেনো মেয়ের জীবন নিয়ে ছিনিমিনে খেলে কেনো এদের বিচার হওয়া ইচুত সবার মতা মত জানায় বেন পিল্জ,0,entertainment
এইসব ছবি দেখলে মনে খারাপ হয়েযাই আগের বাংলা মুভি দেখলেই ভালোলাগতো এরাকি হিরো না গরু ভাই পরিচালকএদেরদিযে ছবি করালে টাকা বাচে এরচাইতে গরু ঘাস কাটেন তাইতো আজ বাংলাদেশের চলচ্চিত্রেরকে সবাই গিননাকরে,0,entertainment
কন সালায়রে দিচ্চত এই ভূয়া খবর।,0,entertainment
সূজিত দাদা বেশ মজা পাইছে<br />যেহেতু ভাবি রূপী বৌদি এখনো ভার্জিন😆😆😆,0,entertainment
যারা ভাবছে নিশো আছে এই নাটকে তাদের কে বলছি <br />নিশো শুধু একটা সিন এই আছে<br />ফায়ার সার্ভিস এ যে লোকটা মারা গেছে উনার চরিত্র করেছেন নিশো।।,0,entertainment
এত সুন্দর একটা মুভি ২০১৯ এ দেখলাম কি করে। সত্যিই অবিশ্বাস্য।,0,entertainment
নায়কের বন্ধুটা ভাল না।,0,entertainment
আমি আছিমালেশীয়া থেকে,0,entertainment
কি দিলেন ভাই বিচারকের নামে কলঙ্ক এরা।,0,entertainment
আমার মতো কমেন্ট দেখে নাটক দেখে কারা,0,entertainment
এডমিন হালার ঘরের হালা।মা বোনকে গালি খাওয়াতে চাস নাকি।,0,entertainment
আনেক ভালো ছবি আমার কেছে অনেক ভালো লাগে,0,entertainment
নায়ক টাকে পাগল পাগল লাগে।,0,entertainment
আমি কতো ছোট দেখছিলা বড় হয়ে গেছে,0,entertainment
বাংলাদেশের শ্রেষ্ঠ নাইকা আমাদের শাবনূর আপু&quot;অসাধারণ একটা মেয়ে &quot;,0,entertainment
"আসলেই,পুরাই,ফালতু,নাটক",0,entertainment
উপস্থাপকের কথা গুলো ভাল্লাগছে। তবে সে ব্যহায়া এসব কথা তার গায়ে লাগে না।,0,entertainment
"এই সব পালতু ছবি,তৈরি করে কে,,,ঘোড়া আকাশে থেকে জমিন এ আনতে পারে,আর উড়ে পাসাদে যেতে পারে না,,,,হা হা হা হা হা",0,entertainment
আমি বললাম তুমি তো ফকির,0,entertainment
ছবিটা যতো দেখি🤷‍♀🤷‍♀<br />ততো অশ্রুজল 😭😭😭হয়ে পড়ি।,0,entertainment
এই রকম নাটক দেখে আমার বাংলার মানুষ কেন ভালো মানুষ হয়নাভালো মানুয় হতে না পারলে নাটক গুলা অমূল হিন,0,entertainment
বুলবুল আর সালমান শাহ আপনাদের আল্লাহ জান্নাত দান করুন। আপনাদের সকল গুনাহ আল্লাহ তুমি ক্ষমা করে দিও।,0,entertainment
জুতা মার শালাদের।,0,entertainment
এ আবার কোন ধরনের ভিডিও,0,entertainment
আপন রক্ত চিনি নাইদুশমন চিনমু কেমনে,0,entertainment
খুব ভাল লাগলো,0,entertainment
তোর দোন কত বড লাগবে,0,entertainment
ইসলাম খেলার জিনিস না ইসলাম কে নাটক সিনেমায় আনা থিক না জারা ইসলাম কে নাটক সিনেমায় আনেন তাদের কে হাত জোর করে বলছি আপ্নেরা ইসলাম কে নাটক সিনেমায় জরায়েন্না,0,entertainment
এই পাগোলের বচ্চাডারে হাতের কাছে পেলে ন্যরা কোরে আলকাতরা লাগিয়ে দিতাম মুখে তো গন্ধো আছেই চুলেও মনে হয় পোকা মাকর বাসা বেদেছে এইটা কিভাবে যাজ ম্যান হয় মুখে দুর গন্ধের আ্যডেই মানায় এই ব্যদোবকে,0,entertainment
"অনেক ভালো লাগলো ,,<br />তোমরা সবসময়ই আমাদের ভালো কিছু দাও ,,,<br />আশা করি ভবিষ্যতে ও এরকমই হবে ,,<br />শুভকামনা রইলো,,,<br />love you bongo bd",0,entertainment
কিভাবে মেয়েকে মেসেজ করবেন। জানতে চাইলে দেখে আসুন ভিডিওটি। ভালো লাগল সাবসক্রাইব করবেন;,0,entertainment
"বাস্তব ভাবে রাজনীতির চরিত্র তুলে ধরা হয়েছে এই নাটকে ,,",0,entertainment
জয় ভাই । আপনার শো ‌তে এমন বা‌জে মে‌য়ে‌কে আন‌বেন আশা ক‌রি নাই । স‌রি জয় ভাই । নি‌জের সম্মানটুকু ধ‌রে রাখুন প্লিজ ।,0,entertainment
এটা কিছু হইলো?🤔,0,entertainment
মরলে কবরের আযাবের সময় বলিস 😑 👊,0,entertainment
জান্নাত সিরিয়াল এর কি হয়েছে???,0,entertainment
"ভাই যদি পারেন তাহলে রুবেলের,, কাঙালী রাজা,, জজ সাহেব,, পলাতক আসামী,, এই ছবি গুলো যে কোন একটা ছবি দেবেন কি ভাই",0,entertainment
নাটকের নামের সার্থকতা<br />নাটকের কলাকৌশলির মাধ্যমে।<br />পরিচালক ও সত্যিই জিনিয়াস👌,0,entertainment
"মোটা হইছে তো কি হইছে,,,<br />অভিনয় এর দক্ষতা আগের মতই আছে,,<br />অনেক সুন্দর লাগছিল শাবনূর আপু কে<br />💜💜💜💜💜💜💜💜💜💜",0,entertainment
"অনেক ভালোএকটা সামাজিক ছবি আমরা চাই এইরকম আরো অনেক ছবি হোক জাতে সমাজের অনেক কিছু পরিবরতন হয়,,আর পরিচালক ভাইকে বলছি আপনি এরকম আরো ছবি আমাদের উপহারদিন জাতে আগামিতে সমাজথেকে কিছু সিখতেপারি,,, আল্লাহ্‌ হাফেজ",0,entertainment
হুমায়ুন ফরিদির প্রথম ছবি সসন্ত্রাস,0,entertainment
বঙ্গ বিডি কে অনুরোধ জানাবো যে সালমান শাহ শাবনূর অভিনীত তোমাকে চাই ছবিটি আপলোড করার জন্য ধন্যবাদ,0,entertainment
নাইকার নাম কি সুন্দরি টার,0,entertainment
দ্বিপু এখন কত বড় হয়েছে কেউ বলতে পারেন? আমার রুপকথার কৌতুহল...,0,entertainment
ভিডিও দেখার আগে লাইক দিলাম,0,entertainment
সেরা ভরা হইছে।,0,entertainment
"এই ছবি দিয়ে অসকার আনবে গাজার খোর নায়ক জাহেদ,,,,,",0,entertainment
এত দেরি করেন কেন দিতে,0,entertainment
আচ্ছা ভাইয়া আমি বুঝলে দেখাও কান্না এসে আপনার প্রতি আমার সাপোর্ট আজীবন থাকবে এমনকি আপনার চ্যানেল প্রতি আমার সাপোর্ট থাকবে সবসময়,0,entertainment
পুলিশের মাথার চুল গুলো এতো বড় কেন,0,entertainment
জসিম রিয়েল বস,0,entertainment
দারুন মুভি দারুন?,0,entertainment
"অনেক মিস করি মহা নায়ক মান্না ভাই কে,",0,entertainment
"বাস্তবতা নিয়ে লেখা নাটকটা,ধন্যবাদ পরিচালক কে❤❤😭😭😭😭😭আমি চাই আমাকে কল দাও,আমি চাই আমাকে কল দিয়ে তুমি কান্না কর,আমি চাই তুমি আমাকে বল তুমি সুখে নেই আমাকে ছাড়া 😭😭😭",0,entertainment
কিন্তু আলেকজান্ডার কে আমার ভালো লাগে তার অ্যাকশন গুলো,0,entertainment
এগুলো কে পিটানো দরকার,0,entertainment
প্রথম ১ ঘন্টা দেখেই মনে হলো বলিউডের বিগ বাজেটের মুভি দেখছি। এরকম মুভি করলে বাংলা মুভি অনেক কম বাজেটেও অনেক সুন্দর মুভি করে এগিয়ে যেতে পারবে।,0,entertainment
কঠিন ছবি অনেক সুন্দর এবং কষ্টের কিছুকারি গর এমন হয়ে যায় টাকার জন্য মানুষকেচিনতে পারে না,0,entertainment
তোক দেখতে মন চায়না রে ভাই। তুই জেন আর ভিডি ও করিশ না ভাই।,0,entertainment
নাওক মান্না মারাগেছে চলচ্চিত্র ও মারাগেছে,0,entertainment
খুব নাইচ ছবি,0,entertainment
বাংলাদেশের নাম্বার ওয়ান ইউটিউবার তৌসিফ আফ্রিদি ইন্টারনেট আমাদের জীবনকে অনেক সহজ করে দিয়েছে 🙂 কাতার থেকে আপনাদের ইউটিউব চ্যানেল ফেসবুক পেজ এখন দেশের গণ্ডি পেরিয়ে সারা পৃথিবীতে লক্ষ লক্ষ প্রবাসীদের মাঝে ছড়িয়ে পড়েছে,0,entertainment
আমার কিছুবলার নাই ছবি দেখে,0,entertainment
ছেলে গুলা রে জেবাবে অপোমান করছে এ ইয়া হবে দোনের রানা দে কবা হানে দোন হবে,0,entertainment
"বিনোদন নেওয়ার কথা বিনোদন নিলাম, কিন্তু বানর থেকে যে মানুষের জম্ম সেটা মানতে পাড়বো না।<br />যাই হক, আসল কথায় আসি বানরআলীযে কতবার রোন্না ঠিক করছে সেটা কে কে খেয়াল করছে🤓🤓",0,entertainment
এই রকম বাজে বিচারকদের বাদ দেওয়া হোক। পালতু কোথাকার,0,entertainment
"খুব সুন্দর মুভি, এক কথায় অসাধারন।",0,entertainment
কি কমু ভাষা বাহিরে পেলছি,0,entertainment
দিপু নম্বার3 ছবি টা হক,0,entertainment
গোসল বিডিও,0,entertainment
সালমান শাহের সাথে কারো নায়ককে তুলোনা করলে ভুল হবে সালমান শাহ একজন রিয়েল ১০০% হিরু ছিল শাকিব জীবনও সালমান শাহের মত হতে পারবোনা বাংলার নায়ক ছিল একজনোই সে হলো সালমান শাহ,0,entertainment
আপনাদের কাছে জজ ব্যারিস্টার শাবানা আলমগীর ভাই এর ছবিটা আপলোড দেন প্লিজ,0,entertainment
আপনারা এত দেরি করেন কিসের জন্য আমাদের বাকি পর্বগুলো তাড়াতাড়ি দিবেন,0,entertainment
"ভাই যদি পারেন তাহলে রুবেলের,,,,<br />,,,, জজ সাহেব,,, পলাতক আসামী,,, পেমিক ডাকাত,,, গোয়েন্দা,,,, লড়াকু সন্তান,,, দিনমজুর,,, নিশ পতি,,, বিচারপতি,,,, আমি শাহেন শাহ,,, আগুন আমার নাম,,, ধর মাস্তান,,, অধিনায়ক,,, মিন্টু আমার নাম,,, লাওয়ারিশ,,, ইনকিলাব,,, বির বিক্রম,,, লড়াই,,, লড়াকু সৈনিক,,, এই ছবি গুলোর যে কোন একটা ছবি দিন ভাই",0,entertainment
"গানগুলো যদি দিতেন !! পরিবেশটা সুন্দর হতো,,,,,,",0,entertainment
"ভাই আপনারা নাস্তিকদের ভিডিও দেখেন কেনো, মোশাররফ করিমতো একটা নাস্তিক, ইসলামের পর্দার বিরুদ্ধে কথা বলে।",0,entertainment
বুনি বড় কইরা ভাইরাল।।। হাইরে বাংলাদেশ,0,entertainment
এই মনে হয় শিখারকিছু আছে। অনেক সুন্দর হয়েছে।,0,entertainment
বাংলাদেশে এমন হাজারও হাতুড়ে ডাঃ আছে যারা কাজের চেয়ে ভাব দেখায় বেশী।,0,entertainment
সময় নষ্ট করে নাটক দেখার চেয়ে বাসায় বসে মশা মারলে ভাল হবে মনে হয়,0,entertainment
অামিও সিনামাতে কাজ করতে চাই,0,entertainment
সত্যি অনেক কালাম ছবিটা দেখে 😂😂,0,entertainment
এটা একটা ফালতু মেয়ে ঠিক আছে 😎 ইনি ইতিমধ্যে বলেছেন যে হাবিব ওয়াহিদ কে বিয়ে করতে চান 😜হাবিব ওয়াহিদের কি মাথা খারাপ যে ইনার মত একটা বেশ্যা টাইপের মেয়েকে বিয়ে করবে😆 তারপর কোন বিজনেসম্যান কিংবা শিল্পপতি এরকম কাউকে উনি বিয়ে করতে চান🤔 আরে একে তো হিরো আলমই বিয়ে করবে না 😭,0,entertainment
এই ছবির হট গান দেন,0,entertainment
"আমার সব প্রিয় বন্ধু দের কাছে অনুরোধ রোইল,, <br /><br />আমারYouTube chanal টা subscribe কর,<br /><br />প্লিজ, আশা করি, বন্ধু দের কাছে, সাহায্য পাব!!!<br /><br />।video ling&quot;:::: <a href=""https://youtu.be/q4ZwdO6NSkI"">https://youtu.be/q4ZwdO6NSkI</a>",0,entertainment
আমি হট ভিডিও দেখতে পছন্দ করি - আমাকে হট ভিডিও লিংক দাও!,0,entertainment
আমার সোনা ডা বানাইচে,0,entertainment
গল্প সুন্দর না তবে নাটকটা দেখেছি তিশার জন্য,0,entertainment
নাটক টা অনেক সুন্দর হয়েছে।।।,0,entertainment
এমপি ম্যাডামের এত বড় 😋 😋,0,entertainment
"বরিশালের লোক ছাড়া, বরিশালের নাটক জমে না।তার পর ও মোটা মুটি ভাল হইছে।",0,entertainment
"এক পায়ের ছবিটা বাকি টুকু কোথায়,ছবি পুরাটা এখনো শেষ হয় নাই ভাই,বাকি অংশ দিলে খুব ভালাে হয়, মতামত জানাবেন",0,entertainment
শাবনুর কেন যে মোটা হয়ে গেল।।।।,0,entertainment
সাকিব খান মানেই অন্য রকম কিছু।,0,entertainment
অনেক কষ্ট এ এবুকে,0,entertainment
কি বেপার ভাই কোনো ছবি পাইতেছি না কেন একটু জানাবেন কি,0,entertainment
"ভাই আপনাদে কাছে অনুরুদ যদি দয়া হয় তাহলে আজকে শাবানাওআলমগীর অভিনিত<br />,,,<br />বাংলার বধু ,বাপের টাকা ,গরীবে বউ ,শাস্তি চাই ,এই চারটি ছবির যে কোন একটা ছবি দেন ভাই আপনাদে কাছে অনুরুদ",0,entertainment
ভিডিওটি ওপেন করা মাত্রই কমেন্টস্ সেকশনে চলে আসলাম 👅😜 কমেন্টসগুলা পড়তে । 😁😀😂😂,0,entertainment
কে কে আমার সাথে এই নাটকটি দেখতে আছেন লাইক কমেন্ট করে সাড়াদেন।<br />জারা বস এর ফ্যান আছ।,0,entertainment
চারজন ডিরেক্টর কে যে জুতা মারতে পারবে সেই হবে মাসুদ রানা,0,entertainment
বাংলা নতুন গান শুনতে পেলাম প্রচুর পরিমাণ,0,entertainment
অনেক ভাল লাকছেনাটক টা,0,entertainment
এক বিনদু ভারটবাসা দাও,0,entertainment
এই ছবিটা দেখেছি অসাধারণ,0,entertainment
"ধন্যবাদ। মাটির কসম, আজকের শয়তান, চাই",0,entertainment
টিজার টি আরো ২মিনিট বাড়িয়ে দিলে কি হতহলে গিয়ে দেখার দরকার হতোনা,0,entertainment
প্রাবাসির টাকা না থাকলে বাংলাদেশ অচল থাকতো।,0,entertainment
এটা হে না। হ্যা।আরবি কে ধংস করার পায়তারা করে,0,entertainment
একটু হলুদ একটু মরিচ রোস্ট টা হয়েছে করা ।। অনেক অনেক ধন্যবাদ তাহসিন ভাই,0,entertainment
"একটা মন চাই,, সুন্দর একটা মনকি আমি পাবো??Aysha +S",0,entertainment
নিজেদেরকে চোরের মত দেখাচ্ছে অথচ তারা অন্যোর চেহারা কে নিন্দা করে।,0,entertainment
এত বাজে হিমু সপ্নেউ এ দেখি নাই...,0,entertainment
আমার প্রিয় নায়ক সালমান শাহ্ 💖💖💖💖💖💖সালমান বসের প্রতিটা মুভি আমার অনেক প্রিয় l love you boss 💖💖💖💖💖💖💖আল্লাহ্ আপনাকে বেহেশ্ত নছিব করুন 👍👍👍👍👍👍👍👍👍👍👍,0,entertainment
দারুন গল্প,0,entertainment
আচ্ছা লাস্টে সাতার কাটার বিষয় টা কি.....,0,entertainment
ফেরদৌস এর হাসিটা অনেক মায়াবী,0,entertainment
"চলুন ভোট হোক,<br />১.মহীয়া মাহি - লাইক<br />২.পরীমনি - কমেন্ট",0,entertainment
মোসারফ <br />ভাই আপনার চুলে তেল দেন্না কেন,0,entertainment
আসলেই গল্পটি ভাল লাগল।<br />👌✅,0,entertainment
ব্যতিক্রমী ও বাস্তবতার চরম রসায়ন।অপূর্ব লেগেছে।।।,0,entertainment
অসাধারন গল্প - অনেক ভালো লেগেছে! (হট সিন গুলি বেশি ভালো লেগেছে!!! হা হা হা ),0,entertainment
"ভাই এই আমাদের বাংলাদেশ,,যেমন জনগণ তেমন পুলিশ,,",0,entertainment
মোশারফ করিম ভাই মানে আমার কাছে অসাধারণ কমেডিয়ান এর মাধ্যমে সমাজের শিক্ষা মূলক নাটক তুলে ধরে মোশাররফ করিম মানে সুপার হিট 😍😍😍লাভ ইউ মোশাররফ ভাই😍😍😍,0,entertainment
সামনে দেশের দুগ্ধ জাতীয় ইস্যুতে বাংলাদেশ রপ্তানি খাতে উন্নত সাধন করবে বলে আসা করি,0,entertainment
"খুবই ভাল লাগছে শাবনুরকে দেখে,,অসাধারন মুভি",0,entertainment
পতিতা,0,entertainment
পুরনো ছবি সামাজিক ছিল কিন্তু রুবেল এখোন সামাজিক ভালো কাহিনির ছবি করেনা ধন্যবাদ,0,entertainment
অনেক কষ্টের মাঝেও মোশাররফ করিমের নাটক দেখা শুরু করলাম।,0,entertainment
"এইগুলা কি আরবি নাকি,,সালারা না পারলে যারা জানে আরবী তাদের থেকে তালিম নে,,,মুখমাফি",0,entertainment
মামুন ভাই পতিতা নিয়া কি নতুন ট্রেন্ড শুরু করলেন?,0,entertainment
ভাই আপনাকে সালাম ভিডিও টা ভালো লেগেছে,0,entertainment
সালা সত্যিই ভয়ংকর,0,entertainment
বাংলাদেশে এমন হিরো আছে আগে জানতাম না ।এই ছবিটা দেখে আমি এই হিরোর ভক্ত হয়ে গেলাম ।iloveumanna,0,entertainment
রহস্য ময় নাটক আমার কাছে ভালো লাগে,0,entertainment
পরকীয়ার ভয়ের কারনে আমি এখনো বিয়েই করছি না। সব মেয়েদের প্রতি মাঝে মাঝে কেন জানি আমর বিশ্বাষ চলে যায়। তার ভাষায় প্রকাশ করতেও আমার একপ্রকারঘৃনা হয়।,0,entertainment
নাগিন,0,entertainment
সুপার স্টার ইলিয়াস কাঞ্চন,0,entertainment
উচিত সিখখা দিছেন ভাই। জার ইমান নাই তার লজ্যাও নাই,0,entertainment
লা হাওলা অলাক্কুয়াতা ইল্লাবিল্লাহিল আলিওল আজিম।এই সমস্ত মেএর জন্য সমস্ত মেএর বদনাম হয়।নোংরা মেয়ে।আমরা চার পাল্লা কাপড় পরি জাতে না বুজাজায় আর এই দেয়াদপ কি বলে।,0,entertainment
বাংলা সিনেমা ভালোই লাগছে কিন্তু প্রবাসে থিয়েটারে প্রচার কেন হয় না,0,entertainment
দোলার কন্ঠ সেই লেগেছে,0,entertainment
শাবনূর আমার জান,0,entertainment
দাড়ি ওয়ালা মালডা কেডা,0,entertainment
তুই এম পি হওয়া আর দেশের গোয়া মারা এক সমান,0,entertainment
প্রেম ভালোবাসা শুধুই কষ্ট,0,entertainment
আমি চাই তাদের জীবন সুখের হক,0,entertainment
নেকেভ,0,entertainment
বালের নাটক দেখলাম সুময় নষ্ট করলাম,0,entertainment
মেয়েটা অসুস্থ মেনটাল,0,entertainment
মুভিটার একশন ছিল খুবই দারুন।,0,entertainment
মুইও বরিশাইল্লা,0,entertainment
ভাই এতদিন তো আমরা খুব অপেক্ষায় ছিলাম এই জিনিসটা দেখার জন্য আপনি এতদিন পরে দিলেন আবার দেখে আমরা অনেক খুশি হলাম আপনাকে অনেক ধন্যবাদ একটু তাড়াতাড়ি বাকিগুলো দিয়ে দিবেন দয়া করে,0,entertainment
তাহসিন ভাই আরেকটু বেশী হান্দাইলে ভালো হইতো,0,entertainment
সানাই নিচতালা ভাড়া দিয়ে দুধু গড়েছে ওকে কে বিয়ে করবে,0,entertainment
বিশেষ করে মেয়েদের এই ছবি বেশি দেখা প্রয়োজন।অনেক কিছু শিক্ষা নিতে পারবে বাস্তব জীবনে। যায় চলার পথে অনেক সাহায্য করবে,0,entertainment
"নো বলিউড, নো ঢালিউড সালমান শাহ ইজ দ্য বেস্ট",0,entertainment
ভালো লাগলো আলোচনা করার মতো অনুষ্ঠান।,0,entertainment
সব গান কাটা কেন।,0,entertainment
হাই মেয়েরা কেউ যদি সুন্দরী নষ্ট বা স্বামী হারা তালাক প্রাপ্ত মেয়ে থাকেন তাহলে আমি তাকে বিবাহ করবো এবং তার বাড়িতে থাকবো এরকম মেয়েরা যদি থাকেন তাহলে আমার সাথে যোগাযোগ করবেন 01400372196,0,entertainment
আমরা প্রবাসীরা এতই অবহেলিত যে আমাদের লাশের ভার কেহ নিতে চায় না কিন্তু বেঁচে থেকে দেশে গেলে অনেকের আবদার আমরা পূরণ করি।ভাল এবং নিরাপদ থাকুক সকল প্রবাসী।,0,entertainment
"এত কিছু যানার পরেওআজ পর্যন্ত কোনো পতিতাকে ভালো হতে দেখলাম না,তারা ইচ্ছা করলেই বিয়ে করে জীবন টা পার করতে পারে",0,entertainment
"আমার ভিডিওটি সবাই দেখবেন আর আমার চ্যানেলটি সবাই সাবসক্রাইব করবেন<br /> Video Link :<a href=""https://youtu.be/eMiJls_xlCU"">https://youtu.be/eMiJls_xlCU</a>",0,entertainment
ও বেশসে,0,entertainment
"এটা কোন ক।হিনী হল, যার এত সুন্দর একটা বাড়ি আছে , ভালো বংশের ছেলে সে আবার বউর গহনা চুরি করে বিক্রি করে বাজার করে কেন?",0,entertainment
ভাল লাগল গল্পটি । বাস্তকব এমন ঘটনা সব সময় ঘটছে।😡😡😡,0,entertainment
ভাই অনেক সময় নিয়ে ভিডিও টি দেকলাম আর অনেক কিছু শিকলাম অসংখ্য ধন্যবাদ ভাই,0,entertainment
সত্যি মুভিটা ভালো লাগলো,0,entertainment
হালারা ইলিয়াস কাঞ্চনের আতঙ্ক ছবি নকল করছে,0,entertainment
ছবিটা দেখে চখে পানি এসে গেল বাল একটা ছবি,0,entertainment
ওরে হিরু আলমের নাম্বার বউ বানানো হক।জাতির চাহিদা।,0,entertainment
একটা ফালতু ছবি দেখে শুধু শুধু সময় নষ্ট করলাম।,0,entertainment
দারুন ছবি। প্রিন্ট ও ভালো,0,entertainment
এই গানে কি এমন জাদু আছে শুনলেই একটা কইরা থাপ্পর খাইতে হই,0,entertainment
আমি অনেক ভালো বাসি নিসো ভাই কে অনেক কিছু শিখতে পেরেছি নিসোকাছ থেকে,0,entertainment
কে কে দুধ খেতে চাও ♥♥♥,0,entertainment
ডেলিভারি কি নরমাল হবে না সিজার,0,entertainment
নাঈম ভাইয়া+অর্পনা আপু=সুপার হিট নাটক,0,entertainment
সাকিবের সঙ্গে অপু কে আমরা আবার দেখতে চাই,0,entertainment
"আগ্রহ নিয়ে দেখার জন্য আসলাম, কিন্তু সাবিলা নুরকে দেখে মেজাজটা নষ্ট হয়ে গেল।",0,entertainment
ভাল লাগার মত একটি র্শটফিল্ম- সবাইকে দেখার অনুরোধ রইল,0,entertainment
সানাই তুই কোন ওয়াজ মাহফিল নিয়ে খারাপ মন্তব্য করবি না তুই কোন মুসলিম মেয়ে না,0,entertainment
খুব ভাল লেগেছে,0,entertainment
কেউ এক বলত বিষ দে,0,entertainment
নিজে যারে বড় বলে বড় সেয়ে নায় লুখে যারে বড় বলে বড় সেয়ে হয় পাগলে কয় কি বর্তমান নায়িকা এর ছেয়ে বুঝি তার জনপ্রিয়তা বেশি পাগলী মা হয়েছে বাবা হয়নি কেউ এটার যেমন কোন মানে নাই তেমন সানাইর কথার কোন মানে নাই সালমান এফ রহমান এর বাসার চাকরানী সানাইর ছেয়ে বড় লুখের মেয়ে হবে,0,entertainment
যতগুলা বাংলা সিনেমা দেখেছি তার মধ্যে অন্যতম একটা পছন্দের ছবি অনেক বার দেখেছি......,0,entertainment
এই মুবির সুহেল লোপার হট সিন এবং হট গান কিনতে চাইলে ইমোতে আসুন ০১৭২২০৮৩৭৮২,0,entertainment
সাবিলার কথা বলার ধরন ভালো লাগে না।,0,entertainment
সানায় তুই একটা নিলজ্জ তুই একটা বেয়দব,0,entertainment
এদের দেখলে বড়ই কষ্ট হয়,0,entertainment
নাম্বার কই,0,entertainment
"হিন্দু মেয়ে টার কথা শুনে অনেক কষ্ট পেলাম, আসলে এটা করা ঠিক হই নাই",0,entertainment
সেভেন মাডার ছবিটি চাই,0,entertainment
এ ধারনের মানুষ দাদার আমলে ছিলো।এখন এমন মানুষ নাই বলে।চলে,0,entertainment
বানাতে ভাল্লাগেনা তো বানিও না কেউ হাত পা ধরে বলছে না যে তুমি এসব ফাতরামি করো,0,entertainment
আমার জীবনে এত নাটক এত শর্ট ফিল্ম দেখছি তার মধ্যে সব থেকে বেস্ট।।।<br />সত্য অসাধারণ 😢😢,0,entertainment
তৌকির আহমেদ কে অসংখ্য ধন্যবাদ এরকম একটি ছবি বানানোর জন্য,0,entertainment
মাসিকের সময় হানিমুন করলে ভার্জিনতো মনে হবে।,0,entertainment
নাইস মুভি খুব সুন্দর লাগলো,0,entertainment
প্লীজ এই ছবির গানগুলো একক ভাবে একটু আপলোড দিন না প্লীজ!,0,entertainment
একসময়ের কমার্শিয়াল হিট ছবি আপসোস ফুল মুভি আপলোড দেয়া হয়নি গান গুলো কাটা হয়েছে,0,entertainment
ভাই আপনাকে অনেক ধন্যবাদ জানাই যে এই ছবিটি দিয়েছেন বলে ভাই আরো কিছু আন কমান ছবি দিন,0,entertainment
ফারিয়ারে পিডাও,0,entertainment
খুব ভালোমুভি,0,entertainment
"গাউ গ্রামের দালাল দের উপরে কিছু করেন, নাইকা বানানো আর বিদেশ ফাটাইয়া দেওয়া মেয়েদেরকে নষ্ট করার আর একটা কারখানা হলোঃ এনজিওর মেয়ে বা মহিলা কর্মি। ৷দুঃখিত",0,entertainment
আমাদের সমাজ ব্যবস্তা এর জন্য দায়,0,entertainment
আমার সাথে কে করতে চাও নাম্বার দাও,0,entertainment
কিছু কিছু ভালোবাসা আছে তার জন্য যদি মরে যায় তবুও সুখ পাওয়া যায়,0,entertainment
বালের মতো হইছে,0,entertainment
ঢেলে দিলো হুম পুরাই ঢেলে দিলো 🤣,0,entertainment
বালের মুভি করতেছে কত কি ডং,0,entertainment
হা হা,0,entertainment
খুবই সুন্দর একটি নাটক,0,entertainment
বিষদাত মুবিটা আপলোড দেন <br />প্লিজ,0,entertainment
আমি পথমে ভাবলাম ফুলের বাড়িতে যেই তিনটি ছেলে দেখলাম সেটি বুঝি চাকরযে ভাবে আচর করছে আর অডার মারছেকিন্তু পরে দেখলাম সেটি ভাইআবার তিন ভাই কাজ ঠিক মতে করেনি বলে শাস্তি ও দিয়েছেএক জনকে বাইরে কানে ধরে দাঁড়িয়ে থাকতে দেওয়া হয়েছেআরেক জনকে কাপড় কাচতে দেওয়া হয়েছেতার পরের জনকে পুরো ঘড় টাকে মুছতে দেওয়া হয়েছেঅথচ এত বড় বাড়িতে একটা কাজের লোক নাইভাইকে কাজের লোক বানিয়ে রেখেছে 😈😈😈,0,entertainment
আমাদের দেশের ছেলেদের এতো দর্জ পারলে না সবাই মিলে জুতা পিটা করতে।,0,entertainment
আমার মতে ওরে তসলিমার মতো দেশ থেকে বের করে দেওয়া হোক,0,entertainment
কেন মা মদ খাওয়া কি খারাপ,0,entertainment
সেই লেভেলের একটা নাটক,0,entertainment
ভাইরে তোরাতো অনন্ত জলিলকে ফেল মাইরা দিলি পুরা বিশ্বে তোগো মতো গায়ক পয়দা হয়নাই তবে হিজড়া সং হিসেবে তোরা এওয়ার্ড পাবি বাঙ্গালী সালের যুদ্ধের কথা ভুইলা গেলেও তোগো গান ভুলবো না তোদের ভাগ্য ভাল যে রহিঙ্গারা এই গান শুনেনাই শুনলে বাংলাদেশে আবার বিদ্রোহো শুরু কইরা ‍দিব,0,entertainment
হা হা হা হা হা হা হা হা কথা গুলো খুব ভাল লগছে,0,entertainment
কি নাটক এটা,0,entertainment
এইটা কমিশনারের বাড়ি,0,entertainment
খানকি,0,entertainment
ভাল কিছু করেন।যেখান থেকে কিছু শিখা যাই,0,entertainment
ওরা অভিনেত্রি নয় ওরা দেহ নেত্রি।,0,entertainment
"অনেক বছর পরে শাবনুর আপুর নতুন মুভি,,😁 <br />আরো নতুন নতুন মুভি চাই শাবনুর আপুর",0,entertainment
কেনো রে চোখে জল এলো..........!!,0,entertainment
মানুষ ভালো দিক গুলো তুলে দরুন খারাপ দিক গুলো মুছে ফেলার চেষ্টা করুন ভালো থাকবেন সবাই,0,entertainment
ধর্মও মুনাজাত নিয়ে ফাজলামো না করলে ভালো হত। নাটক টা দেখে খুব কষ্ট পেলাম।,0,entertainment
"মেয়েটি মায়ের কাছে গিয়ে পাগলের কথা বললো,,বুঝলাম নায়কার মেয়ে এটি,,,কিন্তু বাবা বলছে মা মরা মেয়ে,,এটা কেমন হলো",0,entertainment
এর নাম জীবন,0,entertainment
বিচারক সব গুলোকে জুতা মারা দরকার মানুষের সাথে কি ভাবে কথা বলতে হয় তাই সিখে নাই আর বিচারক হতে এসেছে এদের আগে চ্যানেল আই যে পরিচালনা করছে এবং এই সব গাধা মুর্খ বিচারক এনেছে তাদের আগে পিটানো উছিত। আচ্ছা কেও কি বলবেন ওই সালা দারি ওলাটা কে সে কি করে আমি তো তাকে চিনি না।,0,entertainment
দুই সালাই চাপাবাজ,0,entertainment
আমার পিয়ো নায়করুবেল ভাই,0,entertainment
এমন ভালোবাসার মানুষ এখন আর পাওয়া যায় না,0,entertainment
সুপারহিট অন্তত ভাই,0,entertainment
এদেরকে বিচারক বানাইছে কারা!!!! দেখলেইতো মনে হচ্ছে চোর আর মানুষের সাথে এমন ব্যাবহার করে কেউ নিজের কথাবার্তার ঠিক নাই আর সে অন্যকে জাজ করতেছে। বিচারকদের চেয়ে এখানে আসা সব প্রতিযোগীরাই ভাল ছিল।,0,entertainment
আমার বলার মতভাসা নাই ছবিতে বুজিইয়েছে এই গড় এই সংসার,0,entertainment
শুরু থেকে শেষ করলাম,0,entertainment
"আমার পিও নায়ক মান্না,",0,entertainment
খুবই সুন্দর অসাধারণ ছবি,0,entertainment
"এত সুন্দর অভিনয় আর কোনো নায়ক, নায়িকা কোনো দিনই পারবে না...",0,entertainment
ছোট্ট বেলা উঠানের মাঝে সবাই মিলে দেখেছিলা ছবিটা। আজ অনেক বছর পর আবার দেখলাম আবার সেই ছোট বেলা চলে গেলাম।,0,entertainment
সাব্বাস,0,entertainment
সেরা নায়ক আমির খানের নতুন ছবি চাই,0,entertainment
অপেক্ষায় আছিতারা তারি দেন। দেখে তারপড়ে ভাত খাবো।,0,entertainment
"মনটা খারাপ তাই একটু হাসির জন্য মুভিটি আমার দেখা, গালাগালিপরে করবো 😂😂😂😂🤣🤣🤣",0,entertainment
আমি প্রথম রিয়াজ ও পূর্নিমার সিনামা দেখি মনের মাঝে তুমি । খুব সুন্দর লেগেছিল । তার পর আমি ওই জুরির ফ্যান । যদিও আমি ভারতীয় ।,0,entertainment
আজকাল নটিদিয়া নাটক করায়জানিনা কেমন পরিচালক,0,entertainment
মুনমুন আমার প্রিয় নায়িকা 💖💖,0,entertainment
সাবিলা নুর কে আমার অনেক ভাল লাগে,0,entertainment
"প্রথমে ধন্যবাদ যানায়, নাটকের পরিচালককে, এতসুন্দর শিক্ষনিয় একটি নাটক করার জন্য, এবং একয়সাথে বিনেদন দেবার জন্য, সবমিলিয়ে অনেক সুন্দর নাটকটি,",0,entertainment
দারুন গান,0,entertainment
মালে কয় কি,0,entertainment
নায়কাটার বয়স হয়ছে,0,entertainment
তাওহিদ আফ্রিদির ফ্যানেরা সাড়া দাও,0,entertainment
কঠিন সেক্স ছবি আপলোড দিয়েন ভাই,0,entertainment
"ভাই যদি পারেন তাহলে শাবানা ও আলমগীর অভিনিত,,, বাংলার বধু ,,বাপের টাকা ,,গরীবে বউ,, জজ সাহেব ,,পলাতক আসামী ,,এই ছবি গুলো দেবেন ভাই আপনাদে চেলেনে কাছে অনুরুদ",0,entertainment
দারুন ছবি ভায়া,0,entertainment
শাকিল ভাই আপনি আবার ছবি করেন আপনার মুভি গুলো অসাধারণ,0,entertainment
এমনিতে বাংলাদেশের সিনেমা চলেনা তারপর উলটাপালটা অভিনয় এগুলো কি পরিচালকের নজরে পরে না নাকি অবহেলা,0,entertainment
"রুবেল অভিনীত মুভি সম্পর্ক, ইনকিলাব,লাওয়ারিশ, বিষদাঁত, উদ্ধার। থাকলে দিন।",0,entertainment
শাবনূর কে দিয়েই সব নায়ক ওপরে ওঠছে,0,entertainment
"কাজী হায়াৎ আর মারুফের সিনেমা মানি অন্য রকম,,,",0,entertainment
আবুল মুহিত,0,entertainment
অনেক সুন্দর হয়েছে,0,entertainment
রিয়াজ ভাইয়া আপনি আবার ছবি করেন,0,entertainment
চমৎকার একটি গান,0,entertainment
জয় মান্না ভাই হিরো মান্না নামবার ওয়ান,0,entertainment
শাবনুরি সেরা নায়িকা শাবনুর ছবি করলে হলে যাবো দেখতে তা না হলে আর হলে কখনো যাবো না,0,entertainment
শাবনুল তোমাকে অনেক ভালবাসি,0,entertainment
তুইজে কিসের পাগল আমি বুজতাছি আমার কাচে তরে দিয়া দিমুনে,0,entertainment
সাবেক রেলমন্ত্রি কি আবারও বিয়ে করছেন নাকি ওর দুগ্ধ মন্ত্রি খেতে পারবেনা,0,entertainment
"আমি চিৎকার করে কাঁদিতে চেহেছি,, পারিনি করিতে চিৎকার .....<br />&quot;নির্মমতা কতদূর হলে জাতি হবে নির্লজ্জ &quot;....!!!!",0,entertainment
বাংলা ছবি,0,entertainment
ওয়াও! সেই 👌👌👌 বন্ধুরা আমার চ্যানেল টি করুন লাইক দিন।,0,entertainment
অনন্ত জলিল যখন নদিতে নায়িকার সাথে লাফ মেরে নিচে থেকেপুলিশ কে গুলি করে গুলি লাগবে বুকে কিন্তু দেখছি <br /> নিচে থেকে উপরে গুলি করছে গুলি লাগছে পিঠে এটা কিভাবে সম্ভব,0,entertainment
গান খায়া গাঞ্জা বানাইছস 🤧,0,entertainment
এই মুভিতে আমাদের শৈশব মিশে আছে❤,0,entertainment
এই নদী এখন বর্তমানে কোথায় আছে....,0,entertainment
"মেঘের ওপর আকাশ ওড়ে, নদীর ওপার পাখির বাসা, মনেবন্ধু বড় আশা.....",0,entertainment
সাকিবের জিবনের সেরা গান আমি মনে করি,0,entertainment
😂😂😂😂 হালকার উপজেলা ঝাপসা,0,entertainment
"এই হচ্ছে মেয়েদের আসল রূপ,,,, তারা হঠাত্ বদলিয়ে যাই,,,,",0,entertainment
তাহসিন ভাইয়ের পর আপনিই সেরা রুস্টার😍,0,entertainment
ছিবিটা দেখার অওর কেমন যেন বুকের মধ্যে একটা মোচর দিয়ে উঠল,0,entertainment
জয় ভাই আপনি এদের মতো মেয়ে নিয়ে লাভ করবেনা,0,entertainment
ভাইয়া আপনার এই ভিডিও বানানোর জন্য ধন্যবাদ,0,entertainment
"অনেক দিন পর একটা নতুন পেলাম,,,লাইভ ইউ বস",0,entertainment
হাগার শো কইরা মানুষ কে নিয়ে মগা করে,0,entertainment
"এই ছবিগুলো আমাদের অহংকার, তপু এই ফিল্মে বাড়তি মাত্রা দিল....",0,entertainment
এই ছবিটা অনেকআগে দেখেছিলাম এখনো আমারমনে পরে।,0,entertainment
এখন বুঝি তোমাকে ছারা কেমন লাগে,0,entertainment
বাজেট কম ছিল তাই ডেসাব দুরবল,0,entertainment
সানাই কে পতিতা দের এমপি হিসাবে দেখতে চাই,0,entertainment
কাজি হায়াত এটা কি করলো টিভি ক্যামেরা দিয়া টিভি নাটকরে সিনেমা বানিয়ে ফেল্লো!,0,entertainment
বিচারকেরা এমন ভাব চুদায় মনে হয় ওরাই মাসুদ রানা।,0,entertainment
এই টা থেকে একটা শিক্ষনীয় বিষয় আছে।<br />কি আছে সবাই বলেন দেখি। পারেন কি না,0,entertainment
এই নাটক টা দেখে অনেক মজা পেয়েছি,0,entertainment
আলীরাজের বউয়ের মতো কারো বউ না হয়,0,entertainment
নবাব,0,entertainment
"কিছু ভালোবাসা যতদিন যায় বারে, কিছু ভালোবাসা আছে যতদিন যায় কমে!",0,entertainment
সাইজ নিয়ে কত অহংকার 😂😂😂😂😂😂😂 হায়রে বাঙালী 😂😆😆😂,0,entertainment
চোখের পানি কিছুতেই থামানো গেলো না পড়ে গেলো৷৷৷৷দুইফোটা,0,entertainment
একদিনে নাটকের শুটিং শেষ ।<br />স্টরি কনসেপ্ট ভালো ছিল না 🙂,0,entertainment
খুব ভালো লাগলো আমার বাড়ি পাবনা,0,entertainment
অসাধারণ ছিল নাটকটা।,0,entertainment
এই ছবি শুধু পিংকি চলচিচএ বানাইতে পারে কেননা শরীফ উদিদন খান দিপু সাহেব একজন ভালো পরিচালক,0,entertainment
হায়রে ছবিরে যতখন ববিতা আন্টির শুটিং ছিক ততক্ষনি কাদলাম,0,entertainment
"এমন নাটক আরও আশা করি,,, নির্মাতাদের কাছে.....",0,entertainment
তবে আমার মতে এখানে অন্য চরিত্রের চেয়ে প্রেমের চরিত্র আরো একটু বেশি হলে মনে হয় ভালেঅ লাগতো কারন ভন্ড সেটা প্রমানিত হয়েছে ভালো বাসার জন্য তবে সেখানে ভালা বাসার বেসি পর্ব নাই,0,entertainment
আমার জীবনের মতন,0,entertainment
বাস্তবতার সাথে মিল আছে।,0,entertainment
এখনকা দিনেকি এরক মেযে আছে নাকি,0,entertainment
সাবনুর রিয়াজ মানে সুন্দর সুন্দর গান<br />একদম মনের মত,0,entertainment
আজ যেই সালাই বসের সাথে পাংগা নিছে সেই সালারাই ধরা খাইছে,0,entertainment
নাটকটায় সাউন্ড খুবই কম। ইয়ারফোন ছাড়া শোনা যায়না। দেখে তাই মজা পাচ্ছি না।,0,entertainment
মিথিলা আর তাহসান যদি ডিভোর্সের পর আবার এক হতে পারে। <br /><br />তাহলে আমি আর তুমি কেন পারবো না।,0,entertainment
গুণী পরিচালক এম এম সরকার স্যারের প্রতি রইল বিনম্র শ্রদ্ধা 💕<br />যেখানেই থাকুন ভাল থাকুন,0,entertainment
আমি বাংলা ছবি দেখিনা রিয়াজের ছবি তাই দেখলাম অনেক ভালো লাগলো,0,entertainment
জসীম অনেক বড় অভিনেতা আলমগীরের চেয়ে।,0,entertainment
নাটক টি নোংরা হয়েছে। এমনিতে আমাদের সমাজে অনেক অবনতি হয়ে গেছে। এমন নাটক দিয়ে আর সমাজটা নষ্ট করিয়েননা।,0,entertainment
এরা ২জন এখন কোথায়?বিলুপ্ত হয়ে গেছে কেন???,0,entertainment
বিয়ের ১১ দিন পরেই আমার স্বামী বিদেশে চলে যায় এমন একজন ভালো মানুষ চাই যে আমার দেহ নয় মনটাকে ভালোবাসবে,0,entertainment
ডনরে দেকলে গা শিউরে উটে শালা সালমানশার হত্যাকারি খুনি,0,entertainment
নতুন একটা হানিফ সংকেত,0,entertainment
ভালোবেসে শুধু কষ্ট পেলাম😭😭😭😭,0,entertainment
দুধ এর চাপ খেয়ে তো সাকিব পাগল হয়ে গেলো,0,entertainment
অনেক ধন্যবাদ ভাইয়া আপনাকে,0,entertainment
তুমি আমার জান,0,entertainment
সময় কোথায় জানি হারিয়ে যায় শুধু কথা গুলো থেকে যায়,0,entertainment
প্রভা তুই বাইচা আছস কেমনে?,0,entertainment
জাননাতের পরেরপব গুলো দিন,0,entertainment
"নায়িকার মা,,,র অভিনয়টা খুপ সুন্দর,,,,",0,entertainment
ধুয়ে দিলেন ভাই। 🤣🤣🤣,0,entertainment
"চলচিত্রে র স্ত্রী এইরকম আর ইসলামের দৃষ্টিতে অন্যরকম নাটক টা দেকেছি বাঠ খারাপ লেগেছে কারণ স্বামীর অধিকার আছে স্ত্রী কে শাসন করার কিন্তু একানে পুরুই উল্টো, একটা কথাপরিচালকের মনে রাখা দরকার স্বামীর পায়ের নিচে স্ত্রীর বেহেশত স্ত্রী র পায়ের নিচেনয়",0,entertainment
বাস্তব এর সাথে সব টুকু মিল আছে..👍,0,entertainment
গান ও কমেন্টগুলো দুইটাই চমৎকার,0,entertainment
অনেক আগে দেখেছি। thanks for upload,0,entertainment
ঠিক।বলছেন৷ ভাইয়া,0,entertainment
পভাএকবার এটার সাথে একবার ওটার সাথে পালতু,0,entertainment
"গানগুলো সব তেলেগু মুভির গানের নকল।।।। আর কত দিন এভাবে??? দেখি ছবি টা মুক্তি পাক , পুরা ছবি নকল নাকি মুক্তি পাওয়ার পর বোঝা যাবে।।।।",0,entertainment
আরে হালার পুতেরা আরমানুষ পাছনা ভিডিও বানাতে,0,entertainment
"আরিয়ান ভাই আপনি ভালো না,,কেন আমাদের কে কাঁদান 😍😍😍",0,entertainment
এই সবের জন্য আমরা দায়ী আমাদের সমাজের মানুষ গুলো দায়ী,0,entertainment
"তাকে ৩য় শ্রপনীর, লেবার চরিত্রে যায়, হিমুতে নয়। তার ভোকাল আর্ট মারাত্মক বিশ্রী, চেহারা অত্যন্ত কুশ্রী, এক্সপ্রেশন ৩য় শ্রেনীর, কোন বৈচিত্র নেই, সব নাটকে এক টাইপ এক্সপ্রেসন",0,entertainment
"গরুর হাটে বারি খেয়ে আমি আজ ভাইরাল,,,,বাকি সৌভিকদের বলো কি হবে কাল😂",0,entertainment
বাংলার লাল-সবুজ,0,entertainment
এটা কি হলো,0,entertainment
ত্যানা😂,0,entertainment
আলেকজান্ডার মত ফাইটিং মুভি বাংলা্র কোন নায়ক করতে পারবে না,0,entertainment
কাদালে কাদতে হবেই এটাই স্বাভাবিক,0,entertainment
যেমন কথা বলার ষ্টাইল তেমন চেহারা<br />তোমাকে কখনো ভুলতে পারবোনা,0,entertainment
আমি যখন বিশ্ববিদ্যালয়ে পড়ি আমিও একটা মেয়ের সঙ্গে খুব দুষ্টিমি করতাম কিন্তু মেয়েটা আমাকে একদিন চর মারে আর আমিও সেইদিন থেকে আর ওই মেয়েটার সঙ্গে দুষ্টিমি করি না। <br />কিন্তু সেই মেয়েটাও এখন আমার সঙ্গে কথা বলার জন্য পাগল কিন্তু আমি এখন আর তাকে পাত্তা দেই না।,0,entertainment
জাজেজরাইতো এক একটা জানোয়ার,0,entertainment
"আমরাত সিলেটী, ভাই এরার কথাত আমারার সাথে মিলেনা,",0,entertainment
নায়ক কি ভাব দৰে যেনো ছালমান খান।,0,entertainment
আমার মা আমার জান..,0,entertainment
অনজু ঘোষে ভিডিও গান বা ছবি আপলোড দেন,0,entertainment
শাবনুর মানে নতুন কিছু,0,entertainment
নাটকটা অনেক ভাল লাগলো,0,entertainment
এত নেশা দরেচেরে ভাই সকাল বিকাল সন্ধা যখন সময় পাই তখন দেখি,0,entertainment
"নায়কের অভিনয় দেখে নিজের কাছেই লজ্জা লাগছে,<br /> এদের অভিনয় দেখলে মনে হয় নিজেকেই ধরে বেঁধে চলচিত্রে নিয়ে যায়,,,<br />তবে শাবনূর বেস্ট,",0,entertainment
"জনম জনমের প্রেম এই ছবির নাম শুনে হাসি পেলো, শাকিব অপু প্রেম নিয়েই থাকতেন, বিছানায় যেতে হলো কেনো এবং জার্ত সন্তান জন্ম দিলেন কেনো দুঃখ জনক",0,entertainment
ভাই অনেক সুন্দর হয়েছে,0,entertainment
এই মেয়েগুলার বুকে চাপা কষ্টের কথা গুলো শুনে চোখের পানি আর ধরে রাখতে পারলাম না তোমাদের কাছে খুবই লজ্জিত বোন <br /> কিছু বখাটে ছেলের কারণে হয়তোবা তোমাদের এই পরিণতি<br />দুঃখিত বোন পারলে ওদের কে মাফ করে দিও যে ক্ষমাশীল সেই মহান,0,entertainment
আমি আর কি বলব তোমাদের আমার মাতা কাজকরেনা সুদু বলব ভালথাক তোমাদের জন্য দোয়া করি,0,entertainment
ভাই কি লেখবো বুঝতেছিনা শুধুই চোখে পানি টলবল করতেছে,0,entertainment
এই গানের ছবিটা পেতে চাই!,0,entertainment
নুসরাত ফারিয়া দারুন করছে,0,entertainment
"কবিরাজ আলহাজ্ব আলতাফ হোসেন আজাদী চ্যালেঞ্জ।সরাসরি যোগাযোগ<br />১২ থেকে ৭২ ঘন্টায় সমাধান। সীমিত খরচে কাজ করা হয়। 01977007775<br />টাকা বড় নয় কাজই বড় স্বামী স্ত্রীর অমিল, মনের মানুষকে কাছে পাওয়া, প্রেমে ব্যার্থ, পাওনা টাকা আদায় সংশারে অসান্তী, যে কোন পরকীয়া থেকে ফেরানো, জ্বীন পরির আছর কাটানো, ব্যাবসায় লোকসান, যে কোন কাযে বাধা, মিথ্যা মামলায় জয়ী, শত্রুকে বস করা শত্রুকে শাহেস্তা করা, সন্তানের লেখাপরায় অমনোযোগ, যে কোন নেশা হতে মুক্তি, জমি সংক্রান্ত ঝামেলা থেকে মুক্তি, শনি ও রাহুর গ্রাস থেকে মুক্তি, যাদু টোনা বান মারা- ফিরানো অবাধ‍্য সন্তানকে বাধ‍্য করা, সংসার থেকে সতিন কে তারানো ইত্যাদী তন্ত্র মন্ত্রের মাধ্যমে ১০০ % গেরান্টিতে সমাধান দেয়া হয়। মোবাইল: 01977007775, যাত্রাবাড়ী মোড়, ঢাকা।",0,entertainment
সালমান শাহ্ তুমি এখনোআছো কোটি বাঙ্গালির হৃদয়ে!,0,entertainment
জটিল পুরাই মাথা খারাপ,0,entertainment
"ইসলামে হিল্লা বিয়া বলতে কোন বিয়ে নেই, মিডিয়াতে প্রচারের আগে এই ইনফরমেশন গুলা জানা দরকার আছে প্রচার কারীদের।",0,entertainment
"কম্বিনেশন টা ভাল্লাগে নি, একি চরিত্র দিয়ে এক পরিবারের বাবা মা বানানো, পরবর্তীতে নতুন পরিবারে একি চরিত্র ।চরিত্র সংকট মনে হচ্ছে।",0,entertainment
"ভাই এদের জীবন এদের কাছে ছেড়ে দেওয়া যায় না? বিশ্বে প্রতিদিন কত রিসার্চ পেপার আসছে, কত টেকনোলজিস আসে। কত মানুষ নিজের প্রচেস্টায় কত বর বর কাজ করে বিশ্বে পরিচিতি পায়। সেগুলো নিয়ে ভিডিও করেন। পজেটিভ কিছু ছড়িয়ে দিন। আর নেগেটিভ কিছু ছড়িয়েন না। ওদের জীবন ওদের কাছে ছেড়ে দেন।",0,entertainment
এটাই বাকী ছিল। আওয়ামীলীগের সংরক্ষিত আসনে মহিলা এমপি হলে জনগণ ঘৃনাভরে থুথু দিবে শেখ হাছিনাকে।,0,entertainment
"কি ছায়াছবি,অসাধারণ<br />এই ছবি দ্বিতীয় পার্ট থাকলে অনেক অনেক ভালো লাগতো।",0,entertainment
ধুদ ডেলি কই লিঠার বিক্রি করতে পারো লিঠার কত টাকা,0,entertainment
টাকার জন্য শাবনূর আর কত নিম্ন মানের ছবি করবে,0,entertainment
"অপেক্ষায় রইলাম পর্ব-৮ এর জন্য,,,এই পর্ব টিও অসাধারণ হয়েছে,,দেখে অনেক ভালো লাগলো,,,, সকল দর্শকদের কাছে অনুরোধ আপনারা দেখুন,, দেখে ভালো লাগলে লাইক,,,কমেন্ট ও সেয়ার করবেন,,, আর এই কাহিনী কারও সাথে মিলে গেলে আমরা আন্তরিক ভাবে দুঃখিত,,,, দেখে জানাবেন কেমন লাগলো,,,আপনাদের ভালো লাগাই আমাদের সার্থকতা",0,entertainment
ভয়েস কেমন যেনো...! যেমনই হোক মান্না ভাই বেস্ট....৷,0,entertainment
"ঝন্টু ভাই কই গেলেন, আবার ফিরে আসেন,।",0,entertainment
"ভালো পরিচালনা, অতীত বাস্তবতার রূপান্তর।",0,entertainment
কারা যে দেখে তাহসানের নাটক,0,entertainment
ফালতু মাজে মাজে কথা আসেনা।,0,entertainment
লাইক দেয়ার মত একটা ভিডিও,0,entertainment
"বসের অভিনয় আর অ্যাকশান জটিল তািত তুৃমি আজ বাংলার কিং,সুপারস্টার",0,entertainment
"আনেক ভুতের কাহিনি দেখছি ও শুনেছি,কিন্তু ভয় বা মজা পাইনি আফ্রিদি ।Ilove you so much afridi jan.😍😍😍😍😍😍😍😍😐😐😐😐",0,entertainment
এক পিলিম ৬বার করে দেখিলাম খুব বালো লাগলোআমার পেমেলিরাও কখনো হাসলো কখনো কানলো আর এখন পিলিম করে পেমলিতো দুরে একা চাইতে গিনা লাগে আল্লাহ তোমাকে জাহান্ননাত নচিপ করুক আমিন আর জারা নাইকা চিলো তারা জেন সামনে পিলিম করলে সমাজের সবাই জেন দেখতে পারে এরকু করবেন আমার অনুরোদ,0,entertainment
আর এখনকার কিছু গান শুনলে মানুষ হাটপেল হয়ে যায়।,0,entertainment
মায়ের জন্য যুদ্ধ মুভিটা দেন প্লিজ,0,entertainment
বিদুত একটা কাজের কাজ করছে,0,entertainment
"ভাইয়ের আদর কেমন জানি না,হয়ত খুব মধুর, আমার ত ভাই নাই তাই বুজি না কেমন",0,entertainment
"গল্পটা প্রথম থেকে দেখলে বুঝা যায়, সত্তি খুব কষ্টদায়ক,,, চমৎকার গল্প,,,,,",0,entertainment
ছবিটা অনেক সুন্দর,0,entertainment
আমি বিয়ে করবো কিন্তু খারাপ ত খারাপ থাকে হইতো সাময়িক সময়ের জন্য ভালো হয়।।। এটাই ভয়,0,entertainment
নাউযুবিল্লাহ্,0,entertainment
খুব সুন্দরনাটক,0,entertainment
নাটকের ভুল ত্রুটি ক্ষমার দৃষ্টিতে দেখবেন।।,0,entertainment
রোস্টের ওস্তাদ রাফায়েত ফ্রম শো অফস ঢাকা 😉,0,entertainment
আসলে ভাই আমার কাছে ভাল লাগছে আমরা সবাই মিলেমিশে চেষ্টা করী তাহলে আমাদের দেশ থেকে পতিতা দুর করতে হবে আর পতিতা বন্দ করতে হলে তাদেরকে মারতে হবে যারা অসহায় মানুষকে এনে বেছে দেয় তাদেরকে আমরা দরী সবাই মীলেধন্যাবাদ সবাইকে,0,entertainment
ওচথির গান। মন জানে তুই ছারা কি একা লাগে।,0,entertainment
"একটা গ্লাসে অর্ধেক পানি আছে। সেটাকে কেউ অর্ধেক পূর্ন আবার কেউ অর্ধেক খালি দেখে। এই মুভিটাও তেমনি। ভাল খারাপ যে যেভাবেই নিক না কেন, আসলেই মুন্না জেল থেকে ছাড়া পাওয়ার পর যে দোটানার সৃষ্টি হয় এটা অনেক কঠিন একটা চ্যালেঞ্জ।",0,entertainment
মাসুদ রানা আর হওয়া লাগবে না।এর আগে মইরা ভূত হমু,0,entertainment
এটা অনেক আগের নাটক...,0,entertainment
বিচারক বলদ রাখছে এর নাম বাংলাদেশ,0,entertainment
খুব বেশি খারাপ লাগলও,0,entertainment
"কি বলব,কি ভাবে বুঝাব কত্তো ভাল লেগেছ ?Just Awesome",0,entertainment
আমার মতে রমজান দালালের অভিনয় অসাধারণ হয়েছে ।,0,entertainment
"রাজ মহল,তাসের ঘর,দরদী শত্রু,সোনার সংসার,সাপমু্ক্তি,কশাই,বড় বাড়ীর মেয়ে,ন্যায় বিচার,স্বামীর ঘর, নাগোর দোলা, ছবি গুলো আপদিন।",0,entertainment
"রুবেল এত্ত সুন্দর অভিনয় করেন, যা কিনা ইতিহাস। <br />রুবেল ভাই আপনাকে স্যালুট।আপনি বাংলাদেশের সেরা নায়ক।",0,entertainment
"ভেবে ছিলাম একটু দেখে পরে দেখবো,পারিনি।। 😓😓সব না দেখে থাকতে পারিনি",0,entertainment
আমার প্রিয় একটা ছবি,0,entertainment
সানাই এর আগে বলেছে সে নাকি ভার্জিন না এখন বলছে সে ভার্জিন এই সময়ের মধ্যে কি সেই জায়গাটা সুপার গ্লু লাগাইছে,0,entertainment
"খুব কস্ট দেয় ছবিটা,",0,entertainment
শতাব্দীতে একটা সিনেমা হয়...,0,entertainment
দারুন গান দুজনকেই বেশ ভাল লাগছে। অলটাইম শাকিব খান বেস্ট।।,0,entertainment
আসুন আমরা সবাই পাঁচ নামাজ পড়ি অন্যকে নামাজের তাগিদ দেই ।,0,entertainment
পরা নাটক টাকে নষ্ট করছে একটা ছাগলে,0,entertainment
"এসব হলো চোদার ছবি,নাহলে কি এই ধরনের চোদার কাহিনী নিয়ে ছবি বানায়?",0,entertainment
দুজন লোকই বাংলার সেরা অভিনেতা হুমায়ুন ফরিদি স্যার শালমান শাহ,0,entertainment
ভাই ৮৬ পর্যন্ত দেখছি বাকি পর্ব গুলো বাংলা ডাবিং কবে দিবেন,0,entertainment
মামা গাঞ্জা খাইয়া হাই মামা গাঞ্জা খাইয়া হাই,0,entertainment
আরবী নিয়া এসব উলটা পালটা নাটক করা ঠিক না,0,entertainment
এই মুভি আজীবন দেখা যাবে।,0,entertainment
কমেন্ট পরে দেখা শুরু করলাম,0,entertainment
"নাটকটার নাম হওয়া উচিত ছিলো, পাগল হবো!",0,entertainment
ছবি টা দেখে সবার শিক্ষা নেওয়া উচিত,0,entertainment
ছবির নামটা কি,0,entertainment
আসোলেই সাকিব বাংলার নাম্বার ওয়ান কিং খান,0,entertainment
ভাই এইটা ভালো ছিলো।,0,entertainment
হয়ত ভালো ছিলি আগে বাট তোকে দিয়ে আজে বাজে মুভি বানাবে ওরা তুই কিন্ত ভালো একটার।,0,entertainment
বিচারক নিজে আগে ভাল কাট তার পরে আসিস বিচার করতে,0,entertainment
এক গাড়িতে পরিবারের সবাই যাব্ 😫😫😫,0,entertainment
অসাধারণ হয়ছে ভাইয়া,0,entertainment
"হাইরে আমিন খান এই নায়কের সাথেও সাইড,,,,,মাহি আর আমিন জুটি হয়ে আসলে ছবিটা আরও হিট হত",0,entertainment
দুধের কম্পানিগুলো তাকে খুজছে,0,entertainment
"দয়া করে, জসিমের, হাতকরা, হাবিলদার ডাকাত,বীরবাহাদুর, আদিল,,নিষ্ঠুর,ফাইভরাইফেল,, বিজয়,ভাই জান,ভাই আমার ভাই,,আমি নিরোদশ,,, ইত্যাদি ছবিগুলো দিবেন।",0,entertainment
সবার সেরা মহানায়ক মান্না ভাই,0,entertainment
"তরুলতা আমারও খুব প্রিয় একটা খাবার ছিল,,কিন্তু এখন আর সেই তরুলতা পাই না।",0,entertainment
রংবাজ রাজ্জাক সেরা,0,entertainment
ইলমার সুর ঠিক ছিলনা।,0,entertainment
ভাই আপনার কাছে এতো করে অনুরোধ করছি যদি পারেন তাহলে দয়া করে একটা ছবি দিন ভাই,0,entertainment
ফারিয়া অসাধারণ একটি নাচ,0,entertainment
"আপনার একটা সাবসক্রাইব আমার চ্যানেলটা কে অনেক দুর নিয়ে যাবে,,, দয়াকরে Fazil Team সাবসক্রাইব করে যান নিজের মনে করে।।।",0,entertainment
দিন শেষে দূরবল অভিনয় নিয়ে ছবিটি হবে ফ্লাপ!,0,entertainment
এক বারে অবিশ্বাস্য কথা এটা টাকা খাওয়ার আর এক ফন্দি,0,entertainment
এই মুভির গানগুলো আপলোড করেন,0,entertainment
আরে এদের কি মরার ভয় নেই ছি,0,entertainment
রবীন্দ্রনাথের গল্পটা যেমন সুন্দর ঠিক তেমনি কাজী হায়াতের পরিচালনা এবং মান্নার অভিনয়ও সুন্দর হয়েছে।,0,entertainment
আপনার কাছে এটা আশা করিনি।,0,entertainment
আরে বা চম্যকার মুভি<br />রোবেল ভাইয়ের মুভি মানেই সুপার হিট মুভি,0,entertainment
"এডা ক্যামন হলো,, শেষে সবাই শাবনুরের কাছে মাফ চাইলো😄😄😃😋",0,entertainment
"খুব নাইচ একটা নাটোক,,0096597621520/",0,entertainment
এডমিন ভাই জাবেদ এর নিশান মুভিটা আপলোড দেবেন কেমন,0,entertainment
মারজুক রাসেল কোন অভিনেতা হল তার চেয়ে সিদ্দিক হলে সেই হইত,0,entertainment
পুরোটা ছবি এত সুন্দর লোকেশনে মনে হয় আর কোন সিনেমা বাংলার ইতিহাসে হয় নি,0,entertainment
"খুব কষ্ট পেলাম,,কান্না চলে এসেছে",0,entertainment
প্রতিটা রোগ নিয়ে এরকম নাটক বানানোর জন্য অনুরোধ করছি,0,entertainment
শাবনূর রুবেলের মুভি টা খুবই ভালো লাগছে,0,entertainment
গল্প টি অনেক সুন্দৱ,0,entertainment
একেতো দের সাথে খারাপ ব্যবহার দ্বিতীয়তে আবার ধোকাবাজি চ্যানেল আইয়ের উপযুক্ত বিচার চাই।,0,entertainment
আমি এই প্রথম দেখলাম(03-05-2019) তবে অনেক ভালো লাগলো।,0,entertainment
সাউন্ড এতো কম কেনো,0,entertainment
তৌকির আহম্মেদ বস,0,entertainment
মোশাররফ করিম একজন ভালো অভিনেতা ।কিন্তু ইসলামের বিরুদ্ধে কথা বলে।নিজের পজিশন নিজেই নষ্ট করেছে।তার মাথায় রাখা উচিত ছিল এটা মুসলিম প্রধান দেশ।আল্লাহ তাকে হেদায়েত করবে।।,0,entertainment
আমি দেখেছি এই ছবিটা ছোট বেলা পুরা মুভিটা মনে নেই আজ দেখে নিলাম,0,entertainment
ভাই একটা বন গাড়া তিনি আমার সব মুরগির বাচ্চা খেয়ে ফেলেছে ভাই,0,entertainment
পরিচালকের মাথা মুথা গেছেনাকি!!!! ইভানার সাথে এতো কম বয়সী পোলা যায় ???,0,entertainment
আমাদের শাহরুখ খান আমির খান নাই কিন্তু মান্না ছিলো,0,entertainment
সমাজের এমন কিছুই বাস্তব চিত্র তুলে আনা দরকার.... নিন্দুকের চোখে আঙ্গুল দিয়ে দেখিয়ে দেওয়া দরকার.....সবার শুভ কামনা করছি...,0,entertainment
"এক কথায় অসাধারন,,",0,entertainment
"আমার দেখা শ্রেষ্ঠ ছায়াছবির মধ্যে এটি একটি.,ছবিটা যতবার দেখেছি ততবারিই চৌখ দিয়ে পানি এসেছে",0,entertainment
অনেক স্মৃতি মনে পড়ে গেলো।,0,entertainment
বাংলাছবি দেখে কুকুর চানা,0,entertainment
খুব সুন্দর একটি নাটক,0,entertainment
রুবেল সব গুলো মুভি আমার অনেক ভালো লাগে,0,entertainment
"বিয়ে করার ইচ্ছেতো সেদিনই করুন যে দিন<br /> একটা মেয়ের বিয়ের পর সব কিছু দিতে পারবেন,,, <br /><br />এক নজরে সংক্ষিপ্ত কিছু লিস্ট দেখে নিন।<br />১। লিপিষ্টিক<br />২। লিপ লাইনার<br />৩। নেইল পলিশ<br />৪। ফেস পাউডার<br />৫। আই লাইনার<br />৬। মাসকারা<br />৭। আই শেডো বক্স<br />৮। মেকআপ বক্স<br />৯। শাম্পু ফর হেয়ার<br />১০। কনডিশনার<br />১১। ককোনাট ওয়েল<br />১২। সাবান<br />১৩। সোপ বক্স<br />১৪। পাউডার<br />১৫। পাউডার বক্স<br />১৬। টুথ পেস্ট<br />১৭। টুথ ব্রাশ<br />১৮। চিড়ুনি<br />১৯। তোয়ালে<br />২০। রুমাল<br />২১। টিপ<br />২২। আইবুরু পেনসিল<br />২৩। কাজল<br />২৪। চুলের কিপ<br />২৫। চুলের কাটা<br />২৬। খোপা<br />২৭। বডি লোশন<br />২৮। মেহেদি টিউব<br />২৯। গ্লিটার<br />৩০। রাখি<br />৩১। আয়না<br />৩২। বডি স্প্রে<br />৩৩। পারফিউম<br />৩৪। সেফটিপিন (Golden &amp; Silver)<br />৩৫। চুড়ি (glass, city gold) ৩৬। লাকের নথ (city gold)<br />৩৯। আলতা<br />৪০। চুলের জন্য কাপড়ের ফুল<br />৪১। কুমকুম টিপ<br />৪২। ঘড়ি<br />৪৩। ওড়না<br />৪৪। সেনডেল<br />৪৫। ফেসওয়াশ<br />৪৬। শাম্পু আফটার শাউয়ার<br />৪৭। সান স্ক্রিন বডি লোশন<br />৪৮। মাউথ ওয়াশ<br />৪৯। ফেস রিম<br />৫০। হেয়ার স্ট্রেটনার<br />৫১। ওলিভোয়েল/মেকআপ রিমুভার<br />৫২। মশ্চারাইজার<br />৫৩। টোনার<br />৫৪। মেকাপ রিমুভার কটন<br />৫৫। ওরনামেন্ট ব্যাগ<br />৬৬। ওয়াল ঘড়ি<br />৫৭। রুমের জন্য স্যান্ডেল (নরম)<br />৫৮। মিস্ট<br />৫৯। হেয়ার ড্রায়ার<br />৬০। হেয়ার স্প্রে<br />৬১। নেইল কাটার<br />৬২। ক্যানডেল ৬৩। লেইস<br />৬৪। মোজা<br />৬৫। ট্রলি ব্যাগ<br />৬৬। ভেনেটি ব্যাগ<br />৬৭। পার্টি ব্যাগ<br />৬৮| নেইল পলিশ রিমুভার<br />৬৯। গহনা (গোল্ড + সিটি গোল্ড)<br />৭০। ফেস স্ক্রাব<br />৭১। হিট প্রটেকশন স্প্রে<br />৭২। শাড়ি/লেহেংগা (পার্টির জন্য)<br />৭৩। বোরকা/স্কার্ফ<br />৭৪। বডি ওয়াশ<br />৭৫। আই পেন্সিল (ব্ল্যাক আন্ড<br />হোয়াইট)<br />৭৬। কন্সিলার<br />৭৭। লুস মেকাপ পাউডার.... ইত্যাদি!<br />.<br />এছাড়াও আরো আছে, সে গুলো বলা যাবে না। বাচ্চা হওয়ার আগে হাসপাতালে দৌড়া-দৌড়ি, যাবতীয় ঔষধ তো আছেই......",0,entertainment
এখন আর এধরনে সিনেমা হয় না,0,entertainment
দুদ মেন।,0,entertainment
ভাই কাল ঈদ যদি পারেন তাহলে এমন একটা ছবি দিন যা অন্য কোন চেলেনে নাই বুজেছেন ভাই৷৷৷৷ সকল পবাসী ভাই দের পক্ষ থেকে আপনাকে জানাই ঈদের শুভেচ্ছা ও ঈদ মোবারক,0,entertainment
একদম বেকার,0,entertainment
অনন্ত ভাইয়ের মতো কোটি মানুষের মাঝে মিছে যেতে চাই ।,0,entertainment
অমর প্রেম ছবি আপলোড দেয়ার জন্য ধন্যবাদ ।,0,entertainment
"সাতক্ষীরা আশাশুনির মেয়ে সুতপার ১ম স্টেজ প্রোগ্রাম, মাতালেন সাতক্ষীরা স্টেডিয়া<br />@",0,entertainment
"টিজার অনেক আগেই কতো বার দেখেছি, আর কতো দেখবো,পারলে ফুল মুভিটি ইউটিউবে ছাড়েন?",0,entertainment
বাংলার শাহরুখ খান রিয়াজ........,0,entertainment
ইউটিউবে মুক্তি দেওয়া হবে কবে,0,entertainment
তাহসানের সাথে মেহজাবিন ই জায়না😐<br />আমি দেখি ই না।<br />আর সাবিলা কাবিলা।<br />তাহসানের সাথে তিশা আর মিথিলা আর দূই একটা মমোর😍,0,entertainment
বিচারক গুলা কই পাইছেন ভাই অডিশনের আগে হালকা করে ব্যাবহার শিখিয়ে নিয়ে আসতেন।।।। এতো ভাব কই থেকে আসে সেলিব্রিটি হলেই আপনারা মানুষ হয়ে যান আর কেউ মানুষ না বুঝি ওনারা পারফরমেন্স করতে আসছে আপনাদের থেকে শিখতে আসে নাই।,0,entertainment
"ধন্যবাদ, পূরাতন ছায়াছবি আপলোড দেয়ার জন্য। দয়া করে মাটির মায়া সিনেমাটা আপলোড দিবেন?",0,entertainment
"মম বাংলাদেশের সেরা অভিনেত্রী। <br />ধন্যবাদ, <br />কলকাতা থেকে বলছি।",0,entertainment
বাংলাদেশি নাটক গুলি ভালোই লাগে।<br />কিন্তু কথায় কথায় হিন্দি ভাল্লাগেনা।<br />তাই পুরাটা না দেখেই চলে গেলাম।<br />হিন্দি যদি সোনতেই হয় তাহলে হিন্দি ফ্লিমিই দেখি।<br />দুঃখিত পুরাটা নাটক না দেখার জন্য।,0,entertainment
নাবলে পাললাম না এই মোভিতে সবাই অনেক ভালো অভিনয়করেছেতাদের কে আমার তরোফ থেকে ধন্যবাদ,0,entertainment
মোসারফ আছে বলে আজও নাটক দেখি,0,entertainment
ভগবান শ্রীকৃষ্ণের বলছেন যে বালো বাসা আনোদ ভকতি যেখানে নেই তাৰা কি মানুষ তাই সেখানে নাথা ভালো,0,entertainment
আমি এটা কিছুতে মানতে পারছিনা।,0,entertainment
চ্যানেল আই কে বলছি এইসব গাঁজা খুর জাজ কে ঠাপড়াইয়া নিচে নামান,0,entertainment
বাংলাদেশের প্রতিটা আইটেম গানে ভিলেনকে থাকতেই হবে😂,0,entertainment
রুবেল এর সকল মুভি এর মধ্যে অন্যতম একটি মুভি।,0,entertainment
আচ্ছা কেউ কিছু মনে করবেন না ডাইরেক্টরের সাথে কয়বার সঙ্গ দিলে গিয়ে নাইক্কা বা ছবির সুযোগ মিলে,0,entertainment
এটাকেতো হোমায়রার বাবা মনে হচ্চে তার বাড়ির কাজের লোক।,0,entertainment
সত্যি হৃদয় ছুয়ে গেলো <br /><br />অসাধারন,0,entertainment
"অনেক দিন পরে দেখতে পেয়ে খুব ভাল লাগল <br />, প্রবাস থেকে <br />জুল",0,entertainment
ছবির মাঋ কানে যে নেকেট তাকে সেটা কোথাই ফোল ছবি দিন!,0,entertainment
সানাই কে নিয়ে যারা বাজে মন্তব্য করে আমি তাদেরকে ধিক্কার জানাই জয় ভাইয়া আপনার স্টেজ ডেকোরেশন টা আরেকটু উন্নত করা উচিত।,0,entertainment
অপূর্বের মেয়ে বাবুটা কি যে কিউট কি যে সুন্দর করে কথা বলে এক্কেবারে পাকনা বুড়ি বড় হয়ে একদিন বিরাট অভিনেত্রী হবে।,0,entertainment
নাটক টা দেখার পর ভক্ত হয়ে গেলাম অসাধারণ,0,entertainment
শেষ এ মিল পাইলাম না,0,entertainment
বাংলার বীর বাংলার টাইগার বাংলার মহা নায়ক আসলাম তালুকদার মান্না......,0,entertainment
এরকম দেশাত্মবোধক ছবি দেখলে অনেক ভালো লাগে নিজেকে মনে হয় একটা সৈনিক সৈনিক,0,entertainment
আর কত !!! আর ভালো লাগে না এক টপিক নিয়ে কত যে ভিডিও দেখতে হবে ⚠️,0,entertainment
গাঁজা খেয়ে নাটক বানাইছে,0,entertainment
"নায়কের একশন ঠিক আছে, তবে কথা বা কথার স্টাইল সুন্দর না। নায়িকা বেশ্ট",0,entertainment
"পপির আরো হিট গান আপলোড দেন,,,",0,entertainment
এখন এমন ছবি আর কারে না,0,entertainment
টেলিফিল্ম টা ভালো লাগলো কিন্তুতাজুর হিজলামি টা ভালো লাগলো না।<br />চোখের সামনে ভালো লাগার মানুষ কে নির্যাতন দেখেই গেলো সালা হিজলা,0,entertainment
"আমার,একটা,এমম,পেমিকা,দরকারজেআমারে,রাতেরবেলা,তেলাপিয়ামাচ,বাজিকরি,খাবাইবে,আচেকেউ,এমন,পেমিকা",0,entertainment
কিছু বোঝো না দুধু খাও,0,entertainment
গাঁজাখুরি গল্প গাঁজা খোর ছবি,0,entertainment
কমেডী নাটক সৌদিআরব থেকে,0,entertainment
গান ভালো ই লাগছে।।।,0,entertainment
কথার সাউন্ডথেকে বাজনার আওয়াজ বেশি হয়ে গেছে।নাটক দারুণ,0,entertainment
ভালোবাসা হারায় না। হারিয়ে যায় মানুষ।<br /><br /><br /><br />যাও পাখি বলো তারে সে যেনো ভুলে না মরে,0,entertainment
"মান্না ভাইয়ের কোন তুলনা নাই,",0,entertainment
হা হা হা বুরার সাথে নাটক করে,0,entertainment
সাফা কবিরের নাটক কেউ দেখবেন না,0,entertainment
"জসিমের নাম আগে আসলো কেন, সেতু ভিলেন ছিল।শাবানা জাবেদ, হল নায়ক নায়িকা।সোহেল রানা কেন?",0,entertainment
শালি কি পোশাক পরে মহান আল্লাহ তাওয়ালার কাছে মেহেরবান চায়। এদের যালায় কোথায় যামু,0,entertainment
"নাটকটি অনেক আগেই দেখেছি, কিন্তু এইখানে &quot;ব্যস্ত ডাক্তার&quot; নাটকটা &quot;হাতুড়ি ডাক্তার&quot; নামে চালায় দেওয়ার হেতু কি বুঝলাম না!!!",0,entertainment
দারুণ জবাব,0,entertainment
খুব মিষ্টি,0,entertainment
বড় খানিক হতে পারবি,0,entertainment
এ ছবি কোনদিন পুরনো হবে না ।ভারত থেকে বলছি,0,entertainment
বাংলাএচ,0,entertainment
দোয়া করি বাচচা গুলোর জিবন সুন্দর হয়,0,entertainment
"আমি প্রথমে দেখে মনে করতেছিলাম, কি ভিডিও বানাইছে,কিন্তু শেষের দিকে দেখে মন মানাইতে পারলাম না,চোখে পানি ধরে রাখে পারলা না,<br />যারা এই ভিডিও টা বানাইছে তাদেরকে আমার অন্তরের অন্তস্তল থেকে শুভেচ্ছা ও অভিনন্দন, <br />nice,<br />আমি মোঃ সোহেল রানা,<br />সারিয়াকান্দি,বগুরা,বাংলাদেশ,",0,entertainment
ছবির নাম কি যানতে পারি,0,entertainment
বাজে একটা নাটক। টাইম ওয়াস্ট হইলো হুদাই,0,entertainment
জুতা মারি তকে,0,entertainment
সবি ওই ষ্টার জলসার দোষ,0,entertainment
তাহসান মিথিলার দিকে বার বার তাকিয়ে দেখ ছিলো। বুঝায়ই যায় সে মিথিলা কে কতোটা ভালোবাসতো। কিন্তুু মিথিলার চোখ মুখ দেখলেই বুঝা যাচ্ছে সে তাহসানের প্রতি বিরক্ত 😰😢,0,entertainment
"যারা হাসির কমেডি ভিডিও দেখতে ভালোবাসেন<br />👉ভালোই তো আছি ইউটিউব চ্যানেলটি সাবস্ক্রাইব করুন।<a href=""https://www.youtube.com/channel/UChurzRjbaFw8BvIFQ87luaQ"">https://www.youtube.com/channel/UChurzRjbaFw8BvIFQ87luaQ</a>",0,entertainment
সব গাঞ্জা,0,entertainment
না হেসে পারলাম না। হাহাহা হিহিহি,0,entertainment
অনেক সুন্দর লাগছে এই নাটক টা আরো এমন কিছু ভিডিও চাই প্লিজ প্লিজ প্লিজ,0,entertainment
সবাই কেমন আছো। আমার জন্য দোয়া করবেন আর আমার চেনেল থেকে ঘুরে আসুন,0,entertainment
এই পাগল কে দেশের বাহিরে পাঠিয়ে দিন,0,entertainment
নাটকের নাম,0,entertainment
এটা নাটক না ফাটক,0,entertainment
"অভাব যতই হোক, তারপরও যেনা তো যেনাই।",0,entertainment
চোখের পানি ধরে রাখতে পারি না,0,entertainment
জীবনে একবার পটুয়াখালী গিয়ে বুঝতে পারছি জীবন টা যে কি।আর একবার ভোলা।,0,entertainment
বাংলার সানাই লিওন।,0,entertainment
এর চেয়ে সুন্দর করে আর পাগু রাম ভোকচো গুলারে বুঝানো সম্ভব না😂 ভিডিও এর চেয়ে ভাল আর হয় না জোস ছিল ভিডিও টা ভাই রেস্পেক্ট 👍👌,0,entertainment
বিদেশি কন্ঠর মত লাগে,0,entertainment
"এই মুভি গুলো আপলোড দেন ভাই,,,, স্পর্ধা, মুখোমুখি, আইন আদালত, পলাতক, চাঁদাবাজ, আজকের শয়তান, শিবাগুন্ডা, কৈফিয়ত, ইনকিলাব, অর্জুন, পলাতক আসামী, জ্বলন্ত আগুন, শাস্তির বদলে শাস্তী, সোহরাব রুস্তম, মাটির কসম, মা মাটি দেশ, সত্যবাদী, দরদী শত্রুু, চিরশত্রুু, শত্রুু, চিরঋনী, নাগরানী, আশার প্রদীপ, রাজমহল, রাজদুলারী, রাজসিংহাসন, বাহাদুর, সমাধী, সোনাবউ, বদলা, বিদ্রোহী সন্তান, বিদ্রোহী প্রেমীক, হাসান তারেক, বিচ্ছেদ, আঘাত, আশা, জেলের মেয়ে, ভালোমানুষ, আবেহায়াত, বাগদাদের চোর, দ্যা রাইন, তাসের ঘর, যৌতুক, যোকার, কার পাপে, তৃষ্ণা, প্রেম প্রতিশোধ, প্রতিশোধের আগুন, বাপের টাকা আগুন, ময়নামতি, সংসারের সুখঃ দুখঃ, আদিল, প্রতিবাদ, দিলরুবা, কোবরা, মেহের বানু, আলাদিন আলীবাবা সিন্দাবাদ, সুলতানা ডাকু, হীম্মত ওয়ালী, ডুমুরের ফুল, সহধর্মিনী, বাংলার বধূ, গরীবের বউ, জুলি, চাঁদনী, মন মানেনা, ক্ষ্যাপা নারী, ডাইরেক ফায়ার, স্পটড্যাট, ওরাকারা, অগ্নি সন্তান, মার্শাল হিরো, কাপুরুষ, রাজকুমার,রাজবন্দী, দুই ভাইয়ের যুদ্ধ, বিরোধীদল, আমিই শাহেনশাহ, ঘৃনা, গড়মিল, রক্ত নিশান, আমি গুনাহগার, ভূল বিচার, জুড়া খুন, খুন ও ভালোবাসা, তছনছ, আসামী হাজীর, বসুন্ধরা, লাওয়ারিশ, নিশপতি, নীতিবান,",0,entertainment
"এই ছবির সবার অভিনয় ভালো ছিল, বিশেষ করে সাহেদ খান",0,entertainment
প্রভা মানেই সমুদ্র 😂,0,entertainment
এ কাতার বিশ্বকাপের মূল্যবান জিনিস হয়তো কাতার বিশ্বকাপে কাজে লাগতে পারে চিন্তার বিষয় না এটা👅👅,0,entertainment
এই সিঁদুর সন্ধ্যায় গানটি অনেক ভাল লেগেছিল আমার। এই সিনেমা প্রথম যখন মুক্তি পায় ২০০৫/২০০৬ এর দিকে সম্ভবত তখন আমি সিডি কিনে এটি দেখি।,0,entertainment
রুবেল বাংলাদেশের সেরা এ্যাকশন হিরো,0,entertainment
আমার বাড়ী চুনারুঘাট,0,entertainment
নাটকটা কেমন,0,entertainment
এই মুভির নাম কি,0,entertainment
না।এটিম।চাচা।আপনে।আমার বাবার।বয়েসের।তাই চাচা।বলাম।আপনে।অনেক বছর বেঁচে থাকে ন আমিন দোয়া করি,0,entertainment
বেপোয়া বাংলা ছবি,0,entertainment
পুরা নাটকটাই আবাল মার্কাই ছিল।। হুদাই টাইম লস😒,0,entertainment
রুবেলের নতুন ছবি থাকলে দেন,0,entertainment
এক জান্নাতের কপালে আর কতো দুখ আছে,0,entertainment
আল্লাহ আমাদের পাঁচওয়াক্ত নামাজ পড়ার তাওফিক দান করুন।আমিন,0,entertainment
বিদ্রোহী কবিতা ও গান,0,entertainment
হালারা মেন্টাল ভাই,0,entertainment
রিয়াজের টাকা ছবিটা দেন প্লিজ .,0,entertainment
"মান্নার অভিনয় কেউ পারে না, He is best",0,entertainment
"আমি ইম্পা কে বিষন ভালোবাসি,,,কিন্তু ও আমার মন টা বোঝে না, কি করবো বলেন তো।",0,entertainment
চমৎকার একটা ছবি চমৎকার,0,entertainment
"তোমার হাত পাখার বাতাসে<br />মন জুড়িয়ে আসে,,,,<br />কিছু সময় থাকো আমার<br />পাশে,,,,",0,entertainment
ইট থিরাপি ই সেরা,0,entertainment
বহু বছর আগে ছোট বেলায়এই ছবি টি যখন বিটিভিতে প্রথম দেখছিলাম তখন কিছু সময় পরপর বলতাম যে নায়ক এই বুঝি বড় হবে এই বলে বলে পুরো ছবিটি শেষ হয়ে গেল,0,entertainment
আমি হলে দুই জন কে বিয়ে করতাম,0,entertainment
তাকে এমপি পদ না দেওয়াই ভালো সবচেয়ে ভালো হয় তাহাকে গুগলের মাধ্যমে যাতে ঢুকলে পাওয়া যায় এমপি পদে,0,entertainment
আমি বাংলা ভিডিও খুব একটা দেখিনা কিন্তু এই গানটা প্রশংসার দাবি রাখে । বিশেষ করে ঐশির শুরুতে চিকন ভয়েসটার প্রেমে পড়ে গেলাম,0,entertainment
নায়কের অপ্রয়োজনীয় বারবার চুমা দেওয়া।। এটা বিরক্তিকর।। ফালতু।,0,entertainment
বসের তো এমন ফালতু নাটক করা উচিত না।।,0,entertainment
জানোয়ারেন বাচ্ছাদের পাইলে একবার,0,entertainment
দারুন একটা মুভি ভালো লাগলো দেখে,0,entertainment
নিলয় ভাইয়া আপনাকে অনেক অনেক ধন্যবাদঅনেক ভাল নাটক,0,entertainment
"ভাই আপনার কাছে কি,,, রুবেলের,,,<br />,,,, সম্পক,,, জজ সাহেব,,, পলাতক আসামী,,, দিনমজুর,,, আমি শাহেন শাহ,,, মিন্টু সম্রাট,,, শত্রুু ঘায়েল,,, এক্সিডেন,,, বিচার পতি,,, নিশ পতি,,, মিন্টু আমার নাম,,, সম্রাট,,, আগুন আমার নাম,,, লড়াই,,, লাওয়ারিশ,,,লড়াকু সন্তান,,, ইনকিলাব,,, জুলুমবাজ,,, দংশন,,, লড়াকু সৈনিক,,, ধর মাস্তান,,, এই ছবি গুলোর যে কোন একটা ছবি দিন ভাই আপনার কাছে অনুরোধ করছি",0,entertainment
সুধু আমার না বাংলার প্রিয়া নাইকা শাবনুর আপু আর ওনার আভিনায় দারুন,0,entertainment
ভাই ঠিক আছে। 👍👍💯💯💯,0,entertainment
"শাকিব খানের বাংলা সিনেমার গল্প কাহিনী অনেক দেখলাম, কিন্তু ইসলামিক সিনেমা একটাও দেখলাম না। ইসলামিক সিনেমা করতে পারে না।",0,entertainment
"কোথায় তুমি মা দেখ চেয়ে তোমার মেয়ে সইছে যাতনা দুঃখ বেদনা একদিন যে ছিলো আদুরিনি মা যারে ডাকতো সোনামণি তার জীবন দেখ এখন দুঃখের কাহিনী চোখ ভরা পানি স্বর্ণকারে সোনা পুড়ে গড়ে অলংকার অন্ধকারে আমি পুড়ে হলাম যে অঙ্গার, সুখের প্রদীপ জ্বলে কারো ঘরে আমার ঘর ভাঙে নিঠুর ঝরে একদিন যে ছিলো আদুরিনি মা যারে ডাকতো সোনামণি তার জীবন দেখ এখন দুঃখের কাহিনী চোখ ভরা পানি, কবির খাতা বইয়ের পাতা কত কিছু লেখা আমার ব্যথা আমার কথা কপাল জুড়ে আকা বাদল ঝরে যতো আকাশ থেকে তার চেয়ে বেশি পানি আমার চোখে, তার জীবন দেখ এখন দুঃখের কাহিনী চোখ ভরা পানি,,,, আমার মা বলে আমি এক বড় গাধা লেখা পড়া বুঝিনা আমি মানুষটা আসলে সাদা সিধা কারো মন ভাঙিনা আমার অন্তরে সবার জন্যে আছে মধুর ভালোবাসা আমি রাজা সিংহাসন ছাড়া আমার কোন প্রজা নাই মনের মাঝে ধন দৌলত আছে দেবার ক্ষমতা নাই পাইতাম যদি আমি রাজার ধন হইতাম গরীবের বাদশাহ, প্রেম আছে রে মনের মাঝে প্রেমের মানি বুঝি না স্বপ্ন আছে মনের মাঝে আছে রে ভালবাসা আশা পূরণ কভু হবে না জ্বালিমের দুনিয়াতে যাবো শূন্য হাতে,, তুমি না আসলে ভালো না বাসলে কথা না বললে সাথে না চললে প্রেম বিরাহ শুধু চোখে জল তোমারি প্রেমে বন্ধু পাগল বানাইলারে পাগল তোমায় দেখলে পাগল হয়ে যাই পাগল, নাওনা তোমার বুকে টেনে আমাকে আরো ভাবতে পারি না আমি তুমি হবে আর কারো আজ শুধু নয়নে শয়নে স্বপনে রেখেছি গোপনে আমারি এমনে যে ভাবে সাগরেতে থাকে শুধু জল তোমারি প্রেমে বন্ধু পাগল বানাইলারে পাগল তোমায় না দেখলে পাগল হয়ে যাই পাগল, থাকবো তোমার শুধু আমি সারাটি জীবন জানবে তোমাকে ছাড়া হবে আমারি মরণ রয়েছো অন্তরে ভিতর বাহিরে ঠোঁটের আদরে বুকের গভীরে তোমাকে ঢেকে রাখি শাড়ির আঁচল। তোমারি প্রেমে বন্ধু পাগল বানাইলারে। কত ভালোবাসি আমি তোমাকে সে কথা তুমি জানো না আরো কাছে এসো তুমি আরো ভালোবাসা দিতে, তুমি তো আমারি কারণে জন্মেছ পৃথিবীতে, আমি তো তোমার আছি তুমি তা কেন বোঝনা, জন্মের পরে যদি আবারো থাকে জনম সে দিন রবে তুমি ভালবেসে আমার বুকে।",0,entertainment
ধন্যবাদতৌকিরআহমেদকেএতসুন্দরএকটাছবিউপহারদেওয়ারজন্য৷বাবুভাইয়েরকথানাবললেইনয়কিন্তুকিবলবভাষাখুজেপাচ্ছিনা৷ সেলিমভাইওঅসাধারনছিল৷,0,entertainment
ভালো আর খারাপ নাই গুরু সবাইকে তেল মারে!,0,entertainment
অমর নায়ক আমাদের সিলেট এর অহংকার সালমান সাহ খুব বেশি মিস করি তোমায় মিস ইউ মহা নায়ক ♥♥,0,entertainment
মান্না পাগলী ছবি পাওয়া যাচ্ছে না কেন,0,entertainment
তোমার মত নায়ক আর পাবো না,0,entertainment
দেহ ব্যবসাহি পতিতা নিচ তালা বাড়া দিয়ে উপর তালা বড় করা মজার বিষর,0,entertainment
মুনমুন চমৎকার অভিনয় করেছে।,0,entertainment
শালারা বিচারক না অন্য কিছু,0,entertainment
এইটা কি নাটক হলো কোনো,0,entertainment
তোরা কি নিজে ছবিটা বানিয়ে নিজেরা দেখিস না😂😂,0,entertainment
ভালো লাগছে আমার,0,entertainment
খুব ভালো হইছে ভাইয়া,0,entertainment
ভিডিওটা দেখে কমেন্ট না করে পারলাম না। আমাদের সমাজে মন্দ লোক ভাল লোক দুইটাই আছে।খুব ভাল লাগল শেষ দিকে।,0,entertainment
"এইটা কোন ছবিনা এইটা আজকের দিনের মানুষের জীবনের কাহীনি এই ছবিটা দেকে কিছু শিকার আছে,",0,entertainment
কার কার কাছে ভালো লাগে তারা লাইক 👍👍দিয়ে সারা দাও 😀😀,0,entertainment
বুড়া এখনো বেচে আছে,0,entertainment
শাবনূর ও রিয়াজ ও পূর্নিমা বাংলাদেশ য়ে যতো হিরো ও হিরো হিন আছে সবার থেকে এদের ভালো লাগে,0,entertainment
কিয়ামত খুব কাছে,0,entertainment
এই বলদ গুলাকে রাখার কোনো মানে নেই।,0,entertainment
"খুন ও ভালোবাসা, ছবিটা আপলোড দিয়েন বস",0,entertainment
দোলাতো মনে দোলা দিয়ে গেলে,0,entertainment
নাটকটা আমার কাছে ভাল লেগেছে,0,entertainment
আমার খুব ভালো লাগে অপু আপার আর সাখিব ভাইয়ার বোইদেখতে ভালো লাগে,0,entertainment
মেযেরা খুবই খারাপ বলার বাহিরে,0,entertainment
আগের গানের মতো তেমনটা হয়নি,0,entertainment
একজনকে মারার জন্য এতটাই রাম দা লাগে নাকী? এই জন্যইবলিfilm is not true. Only fake.,0,entertainment
গরিব কে যে মানুষ মনে করেনা ভবিসুতে এই পরিনিতি হয়,0,entertainment
বিচারক হিসেবে রিকশা চালাক একটা আর একটা কাজের মেয়,0,entertainment
অনজু আফা আপনাকে স্বাগত জানাচ্ছি যে এই সব ছবির জন্য ধন্যবাদ জানাচ্ছি এবং ভিন বাজুনর জন্য আমি ডুবাই থেকে বুলবুল ফোন নাম্বার 00971529576350 ও ইমেইল আইডি ইমু ও ওয়াটসব,0,entertainment
আগের ছবি আর এখনকার ছবি,0,entertainment
আসাধারন লাগছে,0,entertainment
স্মৃতি হারায় কিন্তু লেখাপড়া ভুলে না।ফালতু কাহিনী অনেক ছবিতে,0,entertainment
মান্নার মতো নায়ক আর এই বাংলার মাটিতে হবে না,0,entertainment
রুবেল এর ছবি চাই,0,entertainment
খুব ভালো অভিনয় করে মাহিযা মাহি,0,entertainment
সব ঠিক আছে তবে নায়েকা টা হল নারে ভাই হল না,0,entertainment
এই ছবিটার নাম কি ভাই বলতে পারেল,0,entertainment
ভাল না লাগলে বলবে সম্ভব না অপমান করে কথা বলে কেন বিচারকরা দাড়িঁওয়ালা লোকটা বেশি বাজে এইভাবে অপমান করলে নেক্সটে কীভাবে অন্যরা আসার সাহস করবে তাছাড়া জাজগুলার মুখে নিজেই এক্সপ্রেশন নাই নষ্টগুলা।,0,entertainment
ভাই তাকে কে বিয়ে করবে ত বিয়ে যে করবে তার পুষ্টির অবাব হবে না বালতি বরে পুষ্টি পাবে,0,entertainment
এরা কি জাজ,0,entertainment
"শুনে আসছি খাজনার চেয়ে বাজনা ভাল না,, আজ আমি বলছি,, এই ছবির খাজনা চেয়ে বাজনায় বেটার।",0,entertainment
এই রকম ভিডিও আরও চাই!,0,entertainment
"শাকিবের পাশে অপুকে ছাড়া অন্য কাউকে দেখতে চাই না,, অপুই শাকিবের জিবনে বেষ্ট,,,",0,entertainment
বাংলাদেশি এখনকার ছবি গুলা থেকে আগের ছবিগুলা খারাপ হলেও অভিনয় অনেক সুন্দর।,0,entertainment
আর কত অপরাধী...<br />শেষ পর্যন্ত নাটক...<br />😁😁😁<br />like hare,0,entertainment
প্রথম প্রেম কে কেও ভুলতে পারে না ভুলায় তার কিছু অভিনয় কিছু অবহেলা কিন্তু এ সব কিছু মেনে নিয়ে আবার অহ জীবন টা কে সাজিয়া নিতে চলেছে আমার নাটক টা অনেক ভাল লাগছে এগিয়ে চলুন নিশু ভাই আমরা আছি আপনার পাশে...।,0,entertainment
অপূর্ব আর মম ভালো জুটি ভালো লাগে অপূর্ব র অভিনয়ে মুগ্দ করে,0,entertainment
সোনা বন্ধু আমারে দেওয়ানা বানাইলো না জানি কি মন্ত্র পড়ে পাগল বানাইলো,0,entertainment
"কি বলে যে মনের ভাব প্রকাশ করব বুঝতে পারছিনা। অসম্ভব সুন্দর, অতি সাধারন তবু অনন্ন্য অসাধারণ।",0,entertainment
চালিয়ে যাও,0,entertainment
নাটক টি দেখার পর চোখে পানি এসে গেলো,0,entertainment
ভাই রঙ্গিলা এই ছবিটা চাই যে পাই না মিললে ছবিটাকে পাব একটু বলে দিবেন,0,entertainment
সেরা বাবুর্চি❤❤,0,entertainment
আরে ভাই কয় সপ্তাহ হয়ে গেল জান্নাত পর্ব এখনও দেন না,0,entertainment
সিনেমা হলে গিয়ে সর্বপ্রথম আমি এই ছবিটি দেখেছিলাম সাথে ছিল আমার দুই ফুফাতো ভাই একটা সাইকেলে আমরা তিনজন গিয়েছিলাম প্রায় 15-20 কিলোমিটার দূরে সিনেমা হলের নাম ছিল ঝুমুর সিনেমা হল নারিকেল চুরি করে সেই টাকা দিয়ে আমরা তিনজন এই ছবিটা দেখেছিলাম আমার দুই পুপাত ভাইয়ের মধ্যে একটা ফুপাতো ভাই সে এখন আর বেঁচে নেই সেই ইলেকট্রিক শটে মারা গেছে আর আরেকটা ফুফাতো ভাই আছে সৌদি আরব আর আমি অন্য একটা দেশে প্রবাসী আজ সেই দিনটার কথা খুব মনে পড়তেছে যেদিন এ ছবিটা হলে গিয়ে প্রথম দেখেছিলাম আর মনে পড়ে আমার সেই ফুপাতো ভাইয়ের কথা যে অকালে মরে গেছে মাত্র 22 বছর বয়সে<br />মোহাম্মদ ফারুক প্রবাসী,0,entertainment
আগে কমেন্ট দেখি পরে নাটক✌✌,0,entertainment
"নিজের একাউন্ট এ ভিডিওতে view বাড়াবার জন্যই এমনকি সাবসক্রাইব বাড়াবার জন্য তারা নামাজ নিয়ে বর্তমানের YouTube এ বার বার কমেন্ট করছে আসলে আমার মনে হয় তারা একবারও নামাজ পরে না তারাই ৫ওয়াক্ত নামজ এর কথা বলছে,,, সবই স্বার্থের জন্য ভন্ড গুলা এসব কমেন্ট করে",0,entertainment
তর সমান লোক না দেকলে কে দেখবে তর ভোন,0,entertainment
নারিদের হাতে এত অধিকার দেওয়া টিক না আর দিলে আউট তাকেই কবর লওয়া টা কোবি দরকারি তা না হলে জীবণে পছতাবেন ।,0,entertainment
ইসলাম নিয়ে এগুলে বলা ঠিকনা,0,entertainment
ওতো ওর দুধের ভারে নাছতে পারেনা,0,entertainment
"এই ছবিটার কথা ছোট বেলায় শুনেছিলাম<br />আজকে দেখলাম ৬,৯,১৯",0,entertainment
কিছুই লাগেনা শুধু বস লাগে,0,entertainment
একটা গানই বাদ দিয়ে দিলেন।,0,entertainment
বাকি পর্ব গুলো তাড়াতাড়ি বের করেন,0,entertainment
তুই সয়তান,0,entertainment
এই নারীর কারণেই সালমান শাহ্ পৃথিবী থেকে বিদায় নিয়েছে।,0,entertainment
নাটকটি কখন রিলিজ হবে?,0,entertainment
"হায়রে নারী তরে চিনতে বড় ভূল করেছি, তাইতো চখের জ্বলে সেই ভুলের মাসূল দিয়ে যাই। <br /><br />ভালথাকিস,তুই সুখে থাকিস।",0,entertainment
গানের সব ক্র্যাডিট সিংগার এবং সাউন্ড ইন্জিনিয়ারের নিস্বন্দেহে,0,entertainment
আমার সবচেয়ে বেশি পছন্দের নাটক জান্নাত,0,entertainment
হারিয়ে গেছে সব মনের ছবি,0,entertainment
"ছুপার সিনেমা এই রকম কাহিনী এখন কার সিনেমাই দেখা যায় না, সত্যি মান্নার অভিনয় দারুন, আমি ইন্ডিয়া থেকে বলছি, বাংলা দেশের সিনেমা আমি তেমন দেখতাম না কিন্তু মান্নার আম্যাজান সিনেমা দেখার পর আমি ফিদা হয়েগেলাম তার পর থেকে এখন রোজ মান্নার একটা করে সিনেমা দেখি সত্যি মান্না অসাধারন নায়ক, তবে একটাই আপসোস যে তিনি আর বেচে নেই, আর এ রকম সিনেমা পাওয়া যাবে না",0,entertainment
খুবই আবেগী একটা গল্প...,0,entertainment
আচ্ছা ভাই এইটা কোন জায়গায় শুটিং করা হইছে কেউ কি জানেন?<br />খুব যেতে ইচ্ছে করতাছে সেই জায়গায়।,0,entertainment
"বস তুমি থাকবে সারা জীবন মানুষের রিদয়ে,,,,🌰🌽🍔🍗🍖🍖🍅🍆🌽",0,entertainment
রিয়াজ পারবে এই ছবি করতে,0,entertainment
"এই রকম কাহিনী ভালো লাগে না । ভালো ভিডিও , love story , romantic short filmবানান!",0,entertainment
"সবাই দেশি সিনেমা দেখবেন,,,,,,<br />তাহলে সবার কাছে ভালো লাগবে <br />যারা হিন্দি দেখেন তাদের কে বলছি,,,<br />হিন্দি মুভি না দেখে বাংলা সিনেমা দেখেন তাহলে বাংলা সিনেমা দামে উঠবে,,,,,,,,,,",0,entertainment
ভূতের আরো ভয় লাগতে হবে।,0,entertainment
ঐ বুরা একটা লোক দারি সাদা হয়ে গেছে মিথিলা ছি ছি,0,entertainment
তুরস্কের নাটক জান্নাত নাটক কি আর বঙ্গ চ্যানেলে পাব না???,0,entertainment
বাহ! তুমি রাসেল ্‌্‌্‌মাসুদ রানা হতে গেলে ডিম পেড়ে দেখাও,0,entertainment
অপূর্বঅসাধারন এক সামাজিক পরিবার নিয়ে দেখার মত একটি সুন্দর ছবি,0,entertainment
আমার মনে হয় না অই মেয়ের কোন লজ্জা আছে,0,entertainment
আমি কোন প্রকার সিনেমা দেখি না অন্তত জলিলের সিনামা গুলো আমাকে মোকদ্দ করে,0,entertainment
কত সুন্দর পোশাক পরিধান করলো।।।মেহেজাবিন।,0,entertainment
"নাটক টা দেখে অনেক মজা লাগল,,,।<br /><br /><br />আর অনেক কিছু শিখলাম,।<br /><br /><br />ধন্যবাদ,,",0,entertainment
চবিটা অনেক আগেও দেখচি<br />আজকে আবার দেখলাম<br />তখন চবি সম্পর্কে কনো কমেন্স করিনি।<br />তবে এই দরনের চবি করলে বাংলাদেশেরর ফ্রিল্ম মানুষের কাছে আবার জনপ্রিয়তা পাবে।<br />খুব ভালো অভিনয় হয়েচে সবার। <br />অল দ্যা বেষ্ট আরেফিন শুভ,0,entertainment
একেই বলে মুভি হৃদয় কাঁপানো নীরবে চোখের জল,0,entertainment
"ববিতা যেই অভিনয়টা করলো,একজন মায়ের ভাল বাসার তৃষ্ণা এত সুন্দর করে তুলে ধরলো,চোখে জল ছলছল করছিলো,আর বর্তমানে এগুলো ফিল্ম বানাচ্ছে,,,,,অয়াক থ্যু,",0,entertainment
( ),0,entertainment
এটা কি মুভি নাকি কউতুক,0,entertainment
নিজেই বললো ব্রেস্টের ওভার ওয়েটের কারনে পিঠে ব্যাথা হয়। আবার বলে সাইড ইফেক্ট নাই। বদ্ধ পাগল।,0,entertainment
অপু কে আর শাকিব কে খুবই মানাই,0,entertainment
মিস্টার রুবেল ভাইয়া অনেক সুন্দর হয়েছে,0,entertainment
আমি একজন ভারতীয় হিসাবে বলবো নাটক তা অনেক সুন্দর হয়েছে,0,entertainment
"এসো সবাই পাঁচ ওক্ত নামাজ পরি আর আল্লাহকে খুশি করি,,,কে কে আমার সাথে একমত আছে সে সেকমেন্ট করুন",0,entertainment
শভিকের পিছে এই মহামানব দের কোথা থেকে তুলে আনা হয়েছে জাতি জানতে চায়!!!!!!!!!!!!!??,0,entertainment
আহা কি চমৎকার....এই প্রথম মুভিটা দেখতেছি....,0,entertainment
আমি বরাবরই এসব নাটকের ভক্ত,0,entertainment
"নায়করাজ রাজ্জাকের পর যার স্থান, তার নাম ইলিয়াস কাঞ্চন।",0,entertainment
নাটকের শেষ দৃশ্যটা দেখে মনে হলো সত্যিই এটা জীবনানন্দ দাশের জন্মভূমি।,0,entertainment
ছবিটা দেখে হিজরাদের মায়া জন্মাবে সবার।।,0,entertainment
তারাতাড়ি আপলোড দেন ভাই,0,entertainment
দরি ছিরা আছি আমি রুবেলের ছবি সুন্দর,0,entertainment
দুধতো ভালো বড় করলেন। এখন একটা জিনিস বাকি আসে নাভির নিচেরটা ভাই কে বইলেন সেটাও গভীর করে দিবে😂😂😂😂বেশি টাকা লাগবে নাহ।,0,entertainment
সানি লিওনি নিজের একগাছি বাল ছিঁড়ে ফেলে দিয়েছিল। সেই বাল থেকেই নায়লা নাইম জন্মেছিল। 😎,0,entertainment
ভাই আমারে আফ্রিদির নাম্বারটা দিতে পারবেন আমি ওর অনেক বড় বক্ত,0,entertainment
রিয়াজ মানেই হিট,0,entertainment
আর হবেনা বাংলাদেশে মান্নার মতো নায়ক,0,entertainment
নাটকটা সুন্দর ছিল। এক কথায় অসাধারন।,0,entertainment
অনন্তো তুমি কেমন আর তুওমার পাশে মেয়েটা একদম মানায় না হাস্যকর মনে হয়,0,entertainment
বহুবার বলেছি বাপের টাকা ছবিটা দেওয়ার জন্য কিন্তুু পাচ্ছি না।,0,entertainment
এলাট এন্ড লেড এলাট<br />রিগান ভাই তুমি এগিয়ে চলো,0,entertainment
নাটক টা দেখে মনে হল অনেক দিনের আগের নাটক।,0,entertainment
"ভাই যদি পারেন তাহলে,, আলী কেন গোলাম,, ছবিটি দিন ভাই",0,entertainment
নাবার আন সাকিব খান,0,entertainment
শাবনুর আপু জন্য ছবিটা দেখলাম,0,entertainment
আশা করি অনেক সুন্দরহবেনাইচ,0,entertainment
অনেক দিন পর এই মুভিটা দেখলাম ধন্যবাদআপনাকে,0,entertainment
সেই থেকে শুরু দেখা নীলা আপার অভিনয় লাগছে অনেক বেশ আমি দেখব অবশেষ।।।,0,entertainment
এমন নায়ক আর খুজে পাওয়া যাবে না।,0,entertainment
থ্যাংকস ভাই পরিচালক সুন্দরমিল দিছ নাটকটা K.S.A,0,entertainment
সেরা নায়ক আমিন খান,0,entertainment
"প্রেমা তুমি কেমন আছ জানি না,আমার কতা তুমার মনে পরছে কিনা জানি না,আজ কত দিন তেকে তুমার অপেক্ষায় আছি।",0,entertainment
আমার মতো কে কে 2019 এ এইমুভি দেখছলাইকদাও,0,entertainment
শেষ দৃর্শ্য চোখে জ্বল এসে গেল,0,entertainment
ছবি টা খুব সুন্দৱ বাইয়া,0,entertainment
এই ছবির নায়ক দিপু হলো আজকের অরুণ সাহা। অনেক বড় হয়ে গেছে আর সংসার করছে।,0,entertainment
ধন্যাবাদ সাবধান করা জন্যে। 😔😔😔,0,entertainment
আমার চালেজ,0,entertainment
"এই সিনামায় শুরুতে লিখা হয়েছে সর্ব শক্তিমান আল্লাহ,,,, এরা কি জেনা, পাপের সামনেও পবিত্র নাম উচ্চরন করেতেছে কেন?",0,entertainment
আগের নাটক,0,entertainment
নকল বাজ আর কি দেখার বাকি আছে বাংলাদেশর মানুষেরবোকাপাইছে,0,entertainment
"এই ছবিতে রিযাজের অভিনয় হৃদয় ছুয়ে যাওয়ার মতো,,,",0,entertainment
অনেক দিন পর ভালো কিছু দেখলাম। এরকম অভিনয় দেখা যায় না। অসাধারন।,0,entertainment
জান্নাত নাটকের অপেক্ষায় কে কে থাকেন লাইক দিন।,0,entertainment
সেলুট ভাই আপনাকে,0,entertainment
রিহাবে দেওয়া উচিত সব বিচারকে সব কয়টায় ইয়াবা খেয়ে এসেছে ভাইয়া 🎯,0,entertainment
আমার মাই**😥,0,entertainment
শাবনুর আপু মোটা হওয়ার পরেও এত সুন্দর লাগে বর্তমান যুগে একটা নায়িকা ও আমার ভালো লাগেনা শাবনুর নাম্বার ওয়ান এইরকম নায়িকা মনে হয় আর আসবে না বাংলাদেশ আই লাভ ইউ শাবনুর আপু,0,entertainment
সাহেবদের জন্য দেখলাম নাটক টা<br />সাহেদ যে সোনার পাখির সোনা,0,entertainment
সালমান বাংলার অহংকার তুমি আছো লাখো মানুষকে গিরে। আল্লাহ যেন এই মহান মানুষ কে জান্নাতুল ফেরদৌস নাসিব করেন।,0,entertainment
কবে যে দেখতে পাবো মুভিটা খুব মিস করতেছি,0,entertainment
এখন সেই দীপু কেমন আছে...তার কোন ছবি হবে..??,0,entertainment
নিরব সাগর,0,entertainment
পরিচয় দেয়া ছাড়া প্র্যাংক কল করলে সেরকম হতো। <br />সৌভিক 😠👎👎,0,entertainment
আমার খুব পছন্দের একজন শিল্পি কনকচাঁপা৷,0,entertainment
আসলে মেয়েদের ইজ্জতের মূল্য আগে থেকেই কম এইসব উচ্চ বিলাসী হারামিদের কাছে,0,entertainment
শাকিল খান এক জন সুন্দর নায়ক।,0,entertainment
ছবি টা ভালো,0,entertainment
"স্কুল লাইফ এর কথা খুব করে মনে পরল,,এখন কার স্কুল গুলো আর এই অবস্থা নাই।",0,entertainment
বসের সাথে কোন তুলনা হয় না,0,entertainment
রিয়াজ শাবনুর মানেই অসাধারণ জুটি,0,entertainment
শাবনূর ম্যাডাম পিচ্চি পিচ্চি লাগে।,0,entertainment
এইসব কমদামি মেয়েগো জন্য কোন কিছু করা এই জন্য ঠিক নয়,0,entertainment
বন্ধু ছাড়া লাইফ ইম্পসিবল,0,entertainment
ডাঃ মাফুজ গানের সাতে ওনি নাচলে বালহেত,0,entertainment
সালমান শাহ্ শাবনূর আমার প্রিয় জুটি l love সালমান শাবনূর 👍👍👍💓💓💓💓আমার ভালো বাসার জুটি,0,entertainment
"অনেক সুন্দর একটি নাটক দেখলাম। তবে নাদিয়া খানমের ছোট বোন তিশা হা হা হা।তবে এরকম হয় বান্ধবীর ছোট বোনের সাথে প্রেম, কিন্তু বিয়েটা কমই হয়।",0,entertainment
"কে কখন পেরেছে ভালবসা থেকে দূরে সরে থাকতে,,,,,",0,entertainment
দাড়ি ওয়ালা বিচারক রে দেখতে মনে হচ্ছে কতদিন গোসল করে না,0,entertainment
ভালো লাগেছে,0,entertainment
বালের মুভি দেছ,0,entertainment
নাটক গুলো দেখতে অনেক ভালো লাগে,0,entertainment
আপনি কোন,0,entertainment
বাটপারি নাটুক,0,entertainment
অনজুআপুসত্য ইলিয়াসভাইকেভালবাসতো,0,entertainment
"এইটা কোন মুভির ভিডিও স্কীন বলতে পারেন কেউ, প্লিজ",0,entertainment
ইয়া মিথিলার মত সন্তান কারোকে দিও না,0,entertainment
"সবগুলো কথা বুকে লাগছে।হয়তো একদিন খুজবে,তোমার মন ভালো না থাকলে",0,entertainment
"সুটিং কোথায় করা হয়েছে,জায়গার নাম কী?",0,entertainment
আনকমন ছবি দেখলাম ভালোই লাগলো শাবনূর লাগিয়া খারাপ কষ্ট লাগলো!,0,entertainment
"পারলে,,একজবানের,জমিদার,মবি,দেন,,",0,entertainment
ভাই বাংলা বধু ছবি দেন,0,entertainment
আনেক ভালো লাগলো nice,0,entertainment
আহো আহো 😂😂,0,entertainment
"প্রিন্ট ক্রিলিয়ার কম,<br />তার পর ও দেকতেছি,<br />ভাল একটা মুভি,,,,,,",0,entertainment
"হুমায়ন ফরদির, হাংগামা,ও পাংকা মুভি দিয়েন বছ",0,entertainment
আমি ত ভুলে গেছিলাম,0,entertainment
এখানে কি ফুল নাটক টা দেয়া আছে?,0,entertainment
পুরানো ছবি গুলোই ভালো ছিলো....,0,entertainment
কোন পাগল বানাচে এই নাটক,0,entertainment
"খুন ও ভালোবাসা, পাপের শাস্তি, এই ছবি দুটো আপলোড দিয়েন বস",0,entertainment
কি যে ভালো লাগে দেখতেনাটক গুলো,0,entertainment
সানি লিওন ভয়ে পর্ন ছেড়েছে,0,entertainment
ঠিক তো ভালোবাসার নামে একটা বিষয় থাকলে আরো ভালো হতো,0,entertainment
"এক সময় মুভি দেখার জন্য কত পাগল ছিলাম, আর বর্তমান যুগে ইচ্ছায় করেনা",0,entertainment
অপু আপুকে দারুন লাগছে আর নিসাবাইকে সাকিব বাই দোলাই করল খুব বাল লাগলNice job move,0,entertainment
ছিতল হাওয়া,0,entertainment
সময় থাকতে তওবা কর আল্লাহর কাছে। আর নিজেকে পর্দায় রাখো। আর আল্লাহকে ভয় কর।,0,entertainment
কে আছেন আমার মত যে বার বারসালমান শাহ এর ছবি দেখেন।,0,entertainment
এদের শিক্ষাগত যোগ্যতা বিষয়ে জানতে ইচ্ছুক,0,entertainment
অনেক আগের দেখা ছবি এইটি।,0,entertainment
অপু অাপু অাপনিসুন্দর মুভি করার জন্য অামার থেকে শুভেচ্ছারইলো 🌹💘🌺💮🌼💔🍁🍀🌷🌷🌷🌹🌹🌹🌼🌼,0,entertainment
এই ছবিটা দেখারপরেও আমাদের মতো ছেলেরা তো বোজেনা,0,entertainment
ছাগল,0,entertainment
"মৌসুমি আন্টির নতুন ছবির জন্য শুভকামনা রইল, <br />শাবনূর আপু ও শাকিব খান জুটি নতুন ছবি দেখতে চাই, লাভ ইউ শাবনূর আপু,",0,entertainment
"অনেক ভাল একটি নাটক দেখলাম। আসলে বাস্তব জীবনে একটু কস্টতো হবে,তবে তা দুজনকেই শয্য করতে হবে। তানজিন তিশার অভিনয় খুব সুন্দর হয়েছে। আমি তানজিন তিশার একজন বড় ফ্যান।",0,entertainment
"আলেকজান্ডার,জোগো,হিরো",0,entertainment
এরেই নাম ভালবাসা,0,entertainment
খুব ভাল লাগলো নাটক টা......,0,entertainment
এর নাম কি নাটক,0,entertainment
"আবার যদি রিয়াজ ভাইকে ফিরে পেতাম,, মিস ইউ",0,entertainment
সাবিলা তোমার মাঝে খুজে পায় আমার প্রিয়মানুষটাকে.....,0,entertainment
"আমার দেখা প্রথম মুভি কেন হলো না &quot;মৃত্তিকার মায়া&quot; সেই আক্ষেপ কভু মুছঁবে না,,,।। ধন্যবাদ &quot;Bongo movies&quot;",0,entertainment
দোয়া করি আমাদের সোনার বাংলাদেশে এমন সত্যিকারের একজন মানুষ আসবেন। দেশের মানুষকে ভালোবেসে তাদের দুঃখ দূরকরবে।,0,entertainment
নিজেদেরকে খুব বেশি পার্ফেক্ট মনে কর যে ভাবে ওদের সাথে ব্যবহার করেছ মনে হচ্ছে নিজে অনেক বিশাল একটা এক্টর। বালের নাটক দুই একটা করে নিজেকে কি আবাল মনে করে বসে আছ!!! তুমি মেয়েটার একটু কালারটা টিক আছে কিন্তু ওখানে ছেলেরা যেগুলো জায আছে ওদের চেহারাটা নিজের একটু আয়নায় দেখতে বলো সোনা!!! নিজেরা কিভাবে এক্টিং এ আসছ চিন্তা করে দেখ।,0,entertainment
ভাই রে ভাই এতো শর্ট ভিডিও দিয়েন না। চোখের পলকে শেষ হয়ে যায়। প্লিজ টাইম বাড়ান। যেনো চোখ আর ব্রেইন ই শান্তি পায়। ভালোবাসা অবিরাম🖤🖤🖤🖤,0,entertainment
আমার.প্রেয়...নায়াক..মান্না...ভাই,0,entertainment
মাহি আসলেই বেস্ট,0,entertainment
আমার প্রিয় নায়ক। আলেকজান্ডার বৌ,0,entertainment
মিনিটের ভিডিও তে মিনিট ধরে হাসছি 😂😂,0,entertainment
আমাদের বাড়ি বরিশালে ☺<br />লঞ্চে যাতায়াত করার অভ্যাস আছে <br />কিন্তু এমন সিস্টেম না<br />নাটকটা একদম ফালতু 😠,0,entertainment
দীপু তু‌মি কোথায় এখন? তোমার সেই বন্ধুরা কে কোথায় অা‌ছে? কত বড় হ‌য়েছ তোমরা?,0,entertainment
পৃথিবীর শ্রেষ্ঠ ভালবাসা,0,entertainment
বেশ কয়েকবার দেখেছি ছোটো বেলায়..<br />Bt আবার দেখব.. সেভ করে রাখলাম,0,entertainment
"অবসরের পর এই প্রথম ছবি শাবনুরের,শাবনুর এখন ও নায়িকার পাট ছাড়া ছবি করতে রাজি হয় না বাট তার বুঝার দরকার চিলো তাকে এখন নায়িকা মানায় না",0,entertainment
দারুন মজার নাটক,0,entertainment
দেখা শুরু করলাম ভালোই হবে 👌👌👌,0,entertainment
শেষ টা তেমন ভাল হয়নি!👿😎😰,0,entertainment
মিস লংকা ছবিটি দিলে খুশি হতাম,0,entertainment
"কত বছর আগেদেখেছি মনে নেই,আজ আবার কাদলাম।",0,entertainment
"আমারো মণ ভড়ে না,",0,entertainment
যারা মানুষ কে নিজের চেয়ে ও বেশি বিশ্বাস করে তাদের ভাগ্যেই কি এই রকম ঘটে?,0,entertainment
বাকি অংশ গুলো পাইনা কেন ভাই এটা কেমন ব্যবহার শুরু করলেন,0,entertainment
নতুন মুভি কি দেখবে পুশাকের খুবই বাজে অবস্থা…,0,entertainment
রিয়াজ ভাইরে ছবি তুমি শুধু তুমি মুভিটা দিবেন ভাই আপনাদের কাছে অনুরোধ রইলো,0,entertainment
"আমার ভালোবাসা আফরান নিশো ও তানজিন তিশা খুবই চমৎকার অভিনয় করেছেন এবং সুন্দর হয়েছে নাটকটি ভালো লাগার মতো একটি রোমান্টিক গল্প গুলো দিয়ে সাজানো একটি নাটক উপহার পেলাম 👌💚👍 অসংখ্য ধন্যবাদ জানাই রচনা ও পরিচালক ভাই আপনাকে অনেক অনেক ধন্যবাদ 👌💚👍 বাস্তব জীবনের ঘটনা গুলো উপলব্ধি করতে পারেন আপনারা আমাদের সম্মানিত ভালো লাগার জন্য ভালবাসা না থাকলে তাহলে আবেগ দিয়ে বাস্তব জীবনের জুড়ে থাকা ভালবাসা কি সত্যি হতো তা আমি জানি না কিন্তু অচেনা রাজ্যের রাজা বলেছেন আমার ভালোবাসা সার্থক হবে সবাইকে আমার আন্তরিক শুভেচ্ছা জানাও কারণ আমার ভালোবাসায় কোন খুদ নেই এই ধরনের দৃশ্যেইঅভিনয় উপস্থাপনা করে আমাদের মাঝে তুলে ধরা হলো বলে আমি মনে করি সবসময় ফেবারিট বাংলাদেশ নাটক সব দিক থেকেই সেরা 👌💚👍 এবং আমার ভালোবাসার কথা বলেছি আমার ভালোবাসা আফরান নিশো ও তানজিন তিশা খুবই অসাধারণ অভিনয় উপস্থাপনা করে সবসময় ভালো লাগে আমাদের বাংলাদেশের সকল ধরনের দৃশ্যে অভিনয় আমার ভালোবাসা কাছে অনুরোধ রইল আমার ভালোবাসার মানুষ গুলোকে নিয়ে আমার ভালোবাসা,, আমি পেশাগত জীবনে একজন ড্রাইভার কিন্তু আমি বিশ্বাস করি আমাদের জন্য ভালো মানুষ এই পৃথিবীতে অনেক আছে কিন্তু আমরা তা ধরাছোঁয়ার বাইরে তবুও আমার ভালোবাসা সার্থক হবে সবাইকে আমার ভালোবাসা অভিনন্দন 👌💚👍",0,entertainment
আরে আমরা ওনার পাগল ফ্যান,0,entertainment
কপালের কারনে দুইজন দুই ভূবনে😔😔<br />Best lyrics💙💙,0,entertainment
গল্প মোটামুটি ভালো<br />তবে আজাইরা নায়িকা আর থার্ড ক্লাস কয়েকটা হিজরা নায়ক নিয়ে ফালতু সব গান<br />এগুলি দেবার প্রয়োজন কি......!!<br />স্টুপিড,0,entertainment
কারো জীবনে এমন ঘটনা যেন না ঘটে।।।,0,entertainment
এই নাটক গুলো অনেক কঠিন,0,entertainment
লহ্ম টাকা কি তা হলে প্রান কোম্পনি দিয়েছে আর পরিচালকরা ব্যাপারটা খুব ভালো ইনজয় করছে,0,entertainment
আপনারা দু জন আমাদের একমাত্র মহামূল্যবান খনিজ সম্পদ! কামড়াকামড়ি কইরেন না গো!,0,entertainment
এই ধরনের নাটক ছারপত্র পায় কেমনে। পরিচালক সহ সকলের শাস্তি হওয়া দরকার।,0,entertainment
"তুই আমাকে তাই ভাবিছ,,এই কথা টা কলিজাই গিয়ে লাগছে",0,entertainment
এই মুভি আমি 20 বার দেখিছি,0,entertainment
তারার তকদির ভালা তাদের সিলেটিরা পাইছে না যদি ফাইতো ফিটিয়া ঠিক করলো অনে,0,entertainment
ছোটবেলার সবচেয়ে পছন্দের ছায়াছবি।,0,entertainment
"দশ হাজার টাকাআবারমেশিন ,,,, 🤔🤔🤔🤔🤔🤔🤔",0,entertainment
তোমাদের গূদ কেরোসীন মার তে হবে,0,entertainment
হাবিব তর মুখে থুতু দিবে,0,entertainment
এই সব বিচারক গাঁজা ভাইজা খাই না কি সিদ্ধ করে খাই,0,entertainment
এরক আরও গান চাই,0,entertainment
মোশাররফ ই সেরা এটা প্রমানীত।,0,entertainment
লাখ কমেন্ট উসল,0,entertainment
মারিয়া নুর মাসুদ রানা নায়িকা😂😂😂 পূর্ণিমা দাদী দিনে দিনে বয়স কমছে😆,0,entertainment
মিথ্যা কথা ঠিকিই তাকে ছাড়া বেঁচে আছো তো গানে মিথ্যা বলো কেনো,0,entertainment
"ভাই যদি দয়া হয় তাহলে শাবান ও আলমগীর অভিনিত,,,, <br />বাংলা বধু,,, গরীবের বউ,,, শান্তি চাই,,, বাপের টাকা,,, এই ছবি গুলো যে কোন একটা ছবি দিন ভাই আপনার কাছে অনুরোধ",0,entertainment
নতুন মুভি লোড দেন,0,entertainment
শাবনুর আপু খুব ভালো লাগছে,0,entertainment
বিচারক গুলি কোন গ্রহ থেকে আমদানি করা হয়েছে,0,entertainment
সাজু ভাইয়ার নাটক গুলো ভালোই লাগে,0,entertainment
ওনাকে যে বিয়ে করবে শেষ,0,entertainment
বলছি দিদি কথাটা দেব হবে। দ্যাব নয়। 🤣😂🤣😂🤣😂😂😂🤣🤣🤣🤣🤣🤣🤣😂😂😂😂😂😂,0,entertainment
"হাই হাই দেখুন মাদ্রাসার ছাত্ররা উস্তাদের কথা মানার জন্য পরিক্ষার আগে আগে করলোটা কি..! শেয়ার করতে পারেন এবং চ্যানেলটি সাবস্ক্রাইব করে আমাদের সাথেই থাকুন <a href=""https://youtu.be/if1Ac9v6xRc"">https://youtu.be/if1Ac9v6xRc</a>",0,entertainment
বাঙ্গালীর গর্ব করার মত নায়ক রুবেল৷,0,entertainment
অনেক দিন তো হইয়ে গেল কিন্তু বাকি পব গুলো তো অনলাইনে আসে নি। কারণ টা কি..?,0,entertainment
পাগল হইচে বিচারক,0,entertainment
প্রথম এ আমার খুব ভালো লেগেছিলো কিন্তু পরে আমার মেয়েটার পতি অনেক ঘৃণা লেগেছে সত্যি মেয়েরা বাস্তবে এমনি হয়??,0,entertainment
নায়ক ফিটেস্ট না,0,entertainment
প্রভা কি সত্যিই অনেক খারাপ,0,entertainment
অনামিকা আমি ও শুধু তোমাকেই চাই তুমি আর কারো নয়,0,entertainment
সালমান শাহ ♥ সেরাদের সেরা ♥,0,entertainment
"এদেশে রাজনৈতিকভাবে কত অন্যায় হচ্ছে! এসব নিয়ে কি টেলিফিল্ম হয়না!!!??? আমার অনুরোধ নিরিহ মানুষের প্রতি যে অন্যয় অবিচার হচ্চে তাদের নিয়ে ছবি করুন, মানুষগুলো জানবে!&quot;!!!!????",0,entertainment
অনেক সুন্দর এই নাটক আর অসাধারণ অভিনয় করেছেন এটি এম শামসুজ্জামান সহ সবাই,0,entertainment
জামালপুর জেলার দেওয়ানগঞ্জ থানার প্রত্যন্ত এলাকার নামবয়ড়া পাড়া... এই এলাকায় মানুষের গুলো অত্যন্ত সহজ- সরল।এই গ্রামে গেলে মনটা জুরিয়ে যায়...কি সুন্দর পরিবেশ...আসবেন এই গ্রাম দেখতে... আমন্ত্রণ রইল....,0,entertainment
বাকি পর্ব গুলা আসে না কেন.......?,0,entertainment
মিস ইউ মহানায়ক মান্না ভাই,0,entertainment
পর্যাপ্ত পরিমানে গাঞ্জা খাইয়াই কিন্তু মাদক বিরোধী গানটা গাইছে 🤣🤣 কি আমার গান আর নয়া নায়কেরে লিয়া তো কিছু কইলাম না 😂😂😂boxod,0,entertainment
সত্যি অসাধারন নাটক।,0,entertainment
"থানা - কালুখালী,রাজবাড়ী আবার যেই বাজারের দৃশ্য সেটা গোয়ালন্দ, রাজবাড়ী। কিন্তু কফিনের উপর ঠিকানা কিশোরগঞ্জের!!!!",0,entertainment
"আমার অনেক অনেক প্রিয় মুভি এটা,এই মুভির টাইটেল গানটা আমার লাগবে",0,entertainment
এই ছবিটা প্রাই ১২ বসর আগে দেখেছিলাম আজকে আবার দেখলামভালই লাগল,0,entertainment
ভাই আপনার কাছে অনুরোধ করছি যদি পারেন তাহলে আজকে একটা পুরনো আন কমান ছবি দিন,0,entertainment
এত নাটক নয় যেনো বাস্তব জীবনের 1টি অংশ তুলে ধরছো তাই তোমাদের সবাইকে অনেক অভিনন্দন ও সুবেচ্ছাগাপোন করিলো,0,entertainment
আমিও বিয়ে করতে চাই😍😍,0,entertainment
জারা নাটক দেক তারা লাইক দিবা,0,entertainment
আপনারা এরখম ফালতু মে কি বলবো,0,entertainment
জীবন থেকে নেয়া অসাধারণ একটা সিনেমা।,0,entertainment
এই জাইগাটা হিমছড়ি অনেক সুন্দর জাইগা।,0,entertainment
ধর্মকে বুড়া আঙুল দেখিয়ে বিয়ে করছেন মিথিলা। কিন্তু ইসলাম ছাড়া মুক্তি নেই অচিরেই আল্লাহ বুঝিয়ে দিবেন।,0,entertainment
"এগুকা কোন বালও হয়না,,",0,entertainment
ভাই এটা কি ছিল?,0,entertainment
সেরা নায়ক মান্না বেস্ট হিরো বাংলার গর্ব,0,entertainment
পুরনো ছবিগুলো ছিল ছবি আর এখনকার ছবিগুলো হল এক প্রকারের ফাইজলামি।,0,entertainment
তোমরা জারা অডিশনে গেছো কি ভেবে গিয়েছিলে তাদের কাছ থেকে ভালো ব্যাবহারের আসায়,0,entertainment
"আমার মতো গরীব ইউটিউবারদের একটু দয়া করুন ভাই, বোন, দাদা ও দিদিরা। ভিডিও গুলো আপনাদের ভালো লাগবে, কথা দিচ্ছি। এই গরীব ছেলের চ্যানেলটি বেড়ে উঠতে এবং স্বপ্ন পূরণে সাহায্য করুন প্লিজ, এটাই আমার ইউটিউব চ্যানেল।",0,entertainment
আমি নটক টা দেখে চোখের পানি ধরে রাখতে পারলাম না তাই বুঝি জীবন টা অনেক কষ্টের একটা পাথর বলে বুঝাতে পারি না,0,entertainment
করছে কি কম,0,entertainment
সুন্দর হয়ছে ভাই।,0,entertainment
কি আর বলবো বলার মতো কোনো ভাষা নেই,0,entertainment
আসলে বিচারকদের নিয়ে নানাবিধ প্রশ্ন ও সমালোচনা হচ্ছে।তা নিয়ে আমি ও এক মত। কিন্তু এই ভিডিও টাতে যিনি উপস্থানা করেছেন ভাই আপনি আগে নিজের কথার ধরণটা আর শুদ্ধ ভাবে বাংলা বলতে শিখেন।তারপর অন্যদের নিয়ে সমালোচনা করতে আসবেন আবাল।।😂😂😂😂😂,0,entertainment
অহ বস.<br /> কি বলবো এক খতায় অসাধারণ! আমরা এই শাকিব খানকে মিস করে যাবো সারা জিবন ইনশাআল্লাহ. ২০১৯/,0,entertainment
ছবি টা দেখে কিছুতেই কান্না থামাতে পারলাম নাছেইম 2 ছেইম প্রাবাসির কাহিনী,0,entertainment
রোমান্টিক মুভি দেন,0,entertainment
সুন্দর কথা ভাইয়া!! সহমত,0,entertainment
এটাই কি ছিলো পতিদান,0,entertainment
"আবোল তাবোল হিস্টোরি,,😏",0,entertainment
প্রভাকে দেখলেই চোখের সামনে কালো ভোদাটা ভেসে উঠে মিনিট ফ্যাক্ট৷ 😁🍆🍆🍆😁😁😁,0,entertainment
এখনও দেখি নাই নাটকটা দেখা যাইক কেমন হয়।,0,entertainment
পাইলাম না পাইলাম তারে আজো খুজিয়া,0,entertainment
"আমি বিয়ের আগে আমার বউটাকে এমনই দেখে ছিলাম, আর এখন সে সবচেয়েবড় লেবা।",0,entertainment
রুনা আপা অনেক ভালো মানুষ .,0,entertainment
এই বেয়াদপ গুলা মানুষকে অপমান করার জন্য এখানে বসেছে আমি হলে তো জুতা পিটা করে আসতাম এদের তোরা তোদের নিজের দিকে তাকা একবার তোদের দেখেই মনে হচ্ছে জংগল থেকে উঠে আসছো অচল পয়সার দল ধান্দা বাজি করার জন্য বসছো এখানে তোরা জর্জ এখানথেকে বের হয়ে মানুষেরা তোদের মা বাবা তুলে গালি দিচ্ছে আর মানুষরাও পাগল হয়ে এসব গরু ছাগল অসব্ভদের কাছে জায় মানুষকে সম্মান করো তবেই সম্মান মিলবে ।।।,0,entertainment
এসব মুভি যত দেখি তত দেখতে মন চাই...<br />আর এখনের মুভিতো বস্তা পচা মুবি,0,entertainment
এরা বিচারক এদের কোন যোগ্যতা আছে বলে আমার মনে হয়না কারন কোন বিচারকের এমন আচারন হইতে পারে না,0,entertainment
গানটা তো বেশ ছিলো,0,entertainment
রিয়াজ বেস্ট ছিল 😍,0,entertainment
অপুকে বাল লাগে না,0,entertainment
বাস্তবতার সাথে অনেক মিল,0,entertainment
বাপের টাকা মুভি চাই আজ।,0,entertainment
পরিচাকক ভাইদের অনুরোদ আপনারা আবারআসেন এইদরনের ছবি বানান আমাদের চলচিরকে বাচান এটাআমার অনুরোদ ভাই,0,entertainment
"কাউকে পুঁজি করে বেশি কিছু করা সহজ নয়, do something by yourself",0,entertainment
একটি শিক্ষা মূলক নাটক<br />খুব ভালো লাগলো,0,entertainment
"বন্ধুত্ব, অচেনা মায়ের ভালবাসা, ছাত্র শিক্ষক সম্পর্ক, কিংবা একজন জ্ঞানী আদর্শ বাবা....জাফর ইকবাল স্যারের অসাধারন কিশোর উপন্যাসের উপর তৈরি এই চলচিত্র জায়গা করে নিয়েছে মনের মধ্যে। ❤",0,entertainment
এটা একটা নাটক হইলো কাহিনিতো নাই কি করবে আল্লার বা জাল্লার বা জা পারে দি নাটক করে,0,entertainment
বাংলার প্রতিটি ঘরে যেন এই রকম ভাই থাকে।,0,entertainment
"হুমায়ূন আহমেদ একজন অফ সংস্কৃতির ধারক বাহক, নাটক টা তার বহিঃপ্রকাশ, মানুষকে ব্যায়ামপ্রতি উদ্বুদ্ধ না করে কাজের প্রতি উদ্বুদ্ধ করলে অনেক ভালো হতো,ব্যায়াম নিশ্চয়ই ভালো, তবে বর্তমান সময়ের মানুষ খুবই অলস কাজ করতে চায় না, একটা বিষয় অবশ্যই মনে রাখতে হবে কাজ করলে আর্থিকভাবে যেমন স্বাবলম্বী হওয়া যায় তেমনি শরীর স্বাস্থ্য ভালো থাকে ব্যায়াম হয়ে যায়।",0,entertainment
আমি নায়ক দেখে শিহরিত,0,entertainment
খুব সুন্দর হয়েছে-----আসলে বর্তমানের অবস্থা এরকমি,0,entertainment
দেখা হয় <br />মনে পড়ে <br />কখনও না কখনও.....,0,entertainment
অনেক অপেক্ষ্যার পরে পেলাম এক কথায় অসাধারণ 👍👍👍👍👍,0,entertainment
অন্নতজলিলভাই মানি সুপার হিট মুভি,0,entertainment
বাংলাদেশে এসব করবার দরকার কী।ডাইরেক্ট লন্ডন অথবা আমেরিকা গিয়ে মুভিতে অভিনয় করলেই ভালো হয়।,0,entertainment
মঝা পাইলাম,0,entertainment
খুব ভালো লাগলো অনেক ধন্যবাদ,0,entertainment
ভালের মুভি গান আর গান,0,entertainment
নায়িকার মেকাপ করা কম হয়ে গেলো না একটু।,0,entertainment
এক কথায় দারুন হইছে,0,entertainment
এদের বিয়ে কচু ✋ পাতার পানির মতো,0,entertainment
এখন এই রকম মানুষপাওয়া যায়good,0,entertainment
হে আল্লাহ তুমি 👉জালিমদের হাত থেকে  হেফাজত কর আমিন।,0,entertainment
খুব ভালো নাঠক,0,entertainment
বাল এইডার ভুলেও গেছি...<br />এত্তো লেইট??<br />হুয়াই ম্যান????,0,entertainment
মান্নার সুলতান ছবিটা দিবেন ভাই,0,entertainment
আমার বস্ মান্না ভাইয়া।,0,entertainment
"জান্নাত এমন একটা সিরিজ, যার মধ্যে কয়েকটা পরিবারের একেবারেই খিচুড়ি অবস্থা। 😂😂😂 <br />হিংসা, ঝগড়া, প্রেম, পরকীয়া সব পাওয়া যায় একই সিরিজে।<br /><br />মোটেও খারাপ লাগছেনা। <br />ডাবিং এ ভালো লাগে দীপক সুমনের কণ্ঠটা। <br />&#39;রুনা, হেনা, জান্নাত, বৃষ্টি, সেলিম&#39; এ কয়েকটা চরিত্র ভালো লাগে।<br />স্মার্ট হিসেবে মাহদীকে ভালো লাগছে।<br />দাজ্জাল আর কূটনী হিসেবে আরজু আর তার মেয়েটা ই সেরা। মেজাজটা বিগড়ে যায় দুটোকে দেখলে। 😞",0,entertainment
দুটো টাকা রোজগার করতে কত নিচে নামতে পারে বাংলাদেশর কিছু মানুষ তো কে না দেখলে বোঝা যাতো না।,0,entertainment
ওর বাস দিয়া ইচিত,0,entertainment
পপ্পপ্পপ্পপ,0,entertainment
সুন্দরএকটা গানআমি অনেক ভার দেখচিআমি ফয়সাল ডুবাই মোবাইল নামবার ০০৯৭১৫২৯৬১৯৫৪২,0,entertainment
গানের মদ্ধে উ লাগিয়ে ফাটাতে পারে নি😂<br />গান টা ভালো ছিল উ না লাগালেও পারতেন,0,entertainment
"কি ভাবে সুখের সংসার করা যায়, শিক্ষা মূলক নাটক বানান ছেলে মেয়েদের বিয়েতে আকর্ষিত করুন প্লিজ",0,entertainment
অকেক সুন্দর,0,entertainment
নায়কটা কেডা,0,entertainment
"রুশো কি টাকার জোরে নায়ক না অভিনয়ের গুণে, না কি ইন্ডাষ্ট্রিতে নায়ক সংকট।",0,entertainment
মেহজাবিন কে শখের মত লাগে😂😂😂,0,entertainment
নাটকটা কবে আসবে ভাইয়া কয় তারিখে,0,entertainment
আজকের ক‍্যাডার মুভিটা দেন প্লিজ প্লিজ ভাইয়া,0,entertainment
বাল,0,entertainment
আপনারা গান কাটেন কেন গান সহমুভি দেন পিলিজ,0,entertainment
যেমন যখন বলবে সব অংগ প্রত্যংগ আছে ত আরে কি বলেন ফারিয়া ম্যডাম এর খুলে দিতে বলেন সব খুলে করে দেখাচ্ছি জনি সিন্স বেকার হয়ে পড়বে ফারিয়া ম্যডাম বর কে ছেড়ে দিবে।সাকা এর কথা ছোটবেলায় আমরা ওটা কেটে ফেলেছি তা সুরঞ্জিত এখন কি ওটা কাটতে চাচ্ছে ।আবার এখানে চেহেরা দেখাতে এসেছ আরে হালার পো কই কি বা একটা গালি দিয়ে হ্যন্ডসাম চেহেরা ও ফিগার আছে তাই এখানে দেখাতে এসেছি কিন্ত বুঝতে পারে নি কিছু বাদর চেহেরার কিছু আবাল চুদা বিচারক হয়েছে।,0,entertainment
"সেই ছোট বেলায় যেমনবিটিভি তেদেখেছিলাম বাড়ির সবাই মিলে আজও অনেক দিন পর বাড়ির সবাই মিলে আমার ল্যাপটপ এ দেখলাম আর সেই ছোট বেলার স্মতি গুলো মনে করলাম আসলেই আগের দিনের ছবির কোন তুলোনা হয় না,",0,entertainment
এই নাটকের নাম সেনোরিতা হয় কেমনে তা আমার জানা নাই!!! স্প্যানিশ ভাষা যারা বুঝেন তারা অবাক হবেন।,0,entertainment
বৃষ্টির কান্নাটি অসাধারণ হয়েছে!!,0,entertainment
এটা কি দুধ দেখানোর বিজ্ঞান????,0,entertainment
এতোদিন পর দিলেন দয়াকরে আর অফ করবেন না,0,entertainment
এই ছবিকে কোনো বিশেষণ দিয়ে বিচার করা যাবে না। এক কথায় দারুণ একটা মুভি। যেমন গল্প তেমন অসাধারন অভিনয় ।,0,entertainment
"মোগো মোশারফ ভাই নাই,তাই কোনো মজাও নাই,,",0,entertainment
"ছবি টি বেশি সময় দেখতে পারলাম না,,, কান্না ঠেকাতে পারিনা,,,০১:৩৬মিনিট পযর্ন্ত দেখছি,,আমি নিজেও জানিনা কিভাবে কান্না এসেছে,,, পুরাটা সময় চোখের জল টপ টপ করে পড়ছে।অসাধারণ,,, বাকি টুকু পরে দেখবো",0,entertainment
পরিচালক মোস্তফা কামাল রাজ বাদে একটা বিচারক কে দেখে তো মনে হয়না যে এরা বিচারকের যোগ্য। বিশেষ করে দাড়িওয়ালা খানকির পোলারে কোন জায়গা থেকে ধরে আনছে। আরে কেউ যদি সিলেক্ট হবার মত যোগ্য না হয় তাহলে তাকে স্ব সম্মানে বিদায় দিলেই তো হয়। এত ভাব চুদানো লাগবে কেন। ভোদায় বাল জালায় নাই বিচারক গিরি চুদাইতে আইছে।,0,entertainment
মেয়েটার চরিত্র নষ্টা।,0,entertainment
খেয়ে দিলো😂😆😂😆😂😆😂😆😂😆😂😆😂😆😂😆😂😆😂😂😆😂,0,entertainment
সাকিবের বিপরিতে যে থাকবে সেই হিট কিছু বলার নাই সাকিব মানেই হিট সিনেমা।,0,entertainment
দাড়িওয়ালা কাকের বাসার মত মাথা এই লোক নাকি আবার বিচারক আমার মনে হয় চ্যেনেল আইর উপর মহলের লোকেরা প্রতিনিয়ত গাঞ্জা খায় গাঞ্জা না খাইলে এই রকম লোকেরে বিচারক বানাইতো না কি,0,entertainment
আমিন খানকে নিয়ে একটা সেনা বাহিনী ভিত্তিক ছবি বানানো যায়,0,entertainment
"এমন গল্প আমাদের সমাজে প্রতিনিয়ত রচনা হয়ে চলছে, এর শেষ কথায়???",0,entertainment
তাহলে এত নাটক করার কি দরকার ছিল,0,entertainment
অনেক মিস করি শাবনূর কে,0,entertainment
এই মুভিটি রিমেক করার দরকার।,0,entertainment
হাহাহাহাহাহাহা মজা পাইলাম,0,entertainment
বিচারকরা অশিক্ষিতের মত আচরণ করছে না হলে সুন্দর ভাবে বলে দিলেই হয় ।,0,entertainment
জয় ভাই আপনরা বেশিভাগ শো আমি দেখি । হিরো আলমকে আপনার শোতে নিয়ে আসছেন সে আসার জোগ্যতা রাখে। কারণ সে তার প্রচেষ্টার এবং কর্মদক্ষতায়ে এগিয় এসেছে এবং তার মনও পরিষ্কার সে একজন সাদা মনের মানুষ। কিন্তু এরকম বাঝে সানাই আপনার স্টুডিওতে আনেছেন যে কিনা বিদেশে গিয়ে ব্রেষ্ট চার্জারি করে নিজেকে বার্জিন দাবি করছে। এই ধরণের সানাইকে এদেশের সামাজিক এবং সুস্থ মস্তিকের মানুষ সামাজিক কীট ছাড়া আর কিছুই ভাবে না।,0,entertainment
ফুল টেলিফিল্ম টা এখন কোথায় পাব। টিভিতে পুরোটা দেখতে পারি নাই।,0,entertainment
"সাবিলা নূর এতো ভালো অভিনয় করে, এক কথায়অসাধারণ ..!!! এতোদিন অনেকেইতাকে নেকামি আর ছেবলামির জন্য hate করতো! বাট এই নাটকটাতে সাবিলা প্রমাণ করেছে যে সে আসলেই একজন দূর্দান্ত অভিনেত্রী!!আর এই নাটকে সাবিলা কে আসলেই অসম্ভব সুন্দর লেগেছে! যেমন দেখতে সুন্দর লেগেছে তেমনই সুন্দর অভিনয় করেছে!!এই নাটক দেখার পর সাবিলার fan কয়েক হাজার বারবে!!!আমি নিজেই তার অভিনয়ের fan হয়ে গেছি!!!এভাবে চালিয়ে গেলে বাংলাদেশের এক নম্বর আসনটিতে বসতে আর বেশিদিন লাগবেনা!!এগিয়ে যাও সাবিলা!!Love you ..❤",0,entertainment
সাবনূর আপু সবার সেরা চলচ্চিত্র অভিনেত্রী ছিলেন আছেন এবং আজীবন থাকবে,0,entertainment
কে যেন বলচে সবাই নাকি বেকার ফাক বয়😌😌,0,entertainment
সেরা অভিনেতা অবশ্যই মোশারফ,0,entertainment
কার অভিনয় আপনাদের সবচেয়ে বেশি ভাল লাগে ???,0,entertainment
এ প্রথম কোনো ছবি দেখলাম পপিকে ধর্ষন করতে পেরেচে কোনো ভিলেন।,0,entertainment
এই পবে সব চেয়ে বেশি হাসছি,0,entertainment
শাবনূর রিয়াজ জুটি অনেক সুন্দর,0,entertainment
ও সানাই আমি মিল্ক এর গাড়ি পাঠিয়ে দিলাম দুধ দিয়ে দিও,0,entertainment
"এত সুন্দর একটা মুভি,যত দেখি ততই আরো ভাল লাগে,অনেক আবেগ জড়িয়ে আছে এই মুভিতে। তারপরও অনেকেই দেখলাম আনলাইক দিয়েছে!তারা মনে হয় নিয়ম রক্ষার্থেই এমনটা করে কারণ সবাই লাইক করলে কেমনে হবে?😌",0,entertainment
"বাংলাদেশের মুভি প্রযোজকরা আপনারা, আমাদের বাংলাদেশের চাইনিজ মার্কা মানুষদেরকে তৈরী করে ওদের নিয়ে কেনো মুভি তৈরী করেন না !!!?.... ওদেরকে নিয়ে চাইনিজ স্টাইলে ভালো মুভি বানিয়ে দেখিয়ে দেন যে আপনারা পারবেন !? &quot;ওদের নিয়ে একবার ট্রাই করে দেখেন না কেনো ?.... &quot;আই অ্যাম সিওর ওদের তৈরী করে নিয়ে মুভি তৈরী করলে ওই মুভি কখনো ফ্লপ হবেনা&quot; &quot;জাস্ট ট্রাই ইট এন্ড ছি&quot; !!! ???.... মুভির জগতের অনন্য নাম হচ্ছে &quot;চাইনিজ কস্টিউম, অ্যানছিয়েন্ট স্টোরি&quot; দ্বারা যে ভাবে ওরা অভিনয় করে একদম সিরিয়াস এবং ওদের অ্যাকশন স্টাইল ও মারধর ফাইটিং সাউন্ড অস্ত্র অস্ত্রের সাউন্ড ভাব ভঙ্গি মারাত্মক ভাবেই বুঝার মতো সুরু হতে সেষ পর্যন্ত , তা দেখতেই বেশ ভালো এবং অপূর্ব, আর প্রথমত তাহাদের কারেক্টার্রা মানে অভিনেতা ও অভিনেত্রী সকলের বডি ফিট !!!?.... &quot;আর আমাদের বাংলাদেশের গুটা মুভি ইন্ডাস্ট্রির সবাই ওরা শুধুই পর্শিধের কপি কাট&quot;!!!?.... আরে মুভির জগতে পারদর্শিতা হতে হলে চাইনিজদের মতো সিরিয়াস মুভি তৈরীতে অব্যাহত হও !!!???......",0,entertainment
আল্লাহ্ আমাদের কে ভালে মুনদু বুজার তিফিক দিন,0,entertainment
অনেক দিন পর শাবনুরের নতুন ছবি দেখলাম।সাবানর পারেই শাবনের পরেই শাবনুর,0,entertainment
এই সব গান কখনো পুরোনো হবে না💞💞💞💞💞,0,entertainment
অনেকদিন পর দেখলাম নাটক টা খুব ভালো লাগলো।,0,entertainment
না দেখে কমেন্ট করলাম মনে হয় ভালো হবে,0,entertainment
জয় ভাইয়ের প্রশ্নগুলা যথেষ্ট ছিল ওরে লজ্জা দেয়ার জন্য কিন্তু ওর ত ওইসব নেই😁😁 আর জয় ভাইকে বলছি এমন তারসিরা মেয়েদের কে কেন আপনি ইন্টারভিউ নিতে আনেন । নিজের সম্মান নষ্ট করবেন না প্লিজ,0,entertainment
এতদিন পর আপনাদের ঘুম ভাংলো?,0,entertainment
অভিনয়কাকেবলেজসিমস্যারজানে,0,entertainment
এই রকম খারাপ ভিডিও দিবিনা,0,entertainment
"যার মধ্যে প্রেম আছে সেই বোঝে এর যন্ত্রণা।।।।। কয়জন আছে সত্যিকারের প্রেমিক ,,,,,,,,,,,,",0,entertainment
ভাই রুবেলের টাইম নাই ছবিটা দিয়েন,0,entertainment
ফিল্মটা ভালই লাগল কিন্ত পপির পোশাকটা ভালো লাগল না,0,entertainment
হাপ নি কি কাইচেন নিচ তলা,0,entertainment
জাজদের কে কে ঘন্টা হিসেবে কানে গলায় থাপরাতে চান লাইক দিয়ে বুঝান,0,entertainment
চিচি,0,entertainment
মান্না মানেই ছবি সুপারহিট,0,entertainment
"জাফর ইকবাল স্যারের কাছে request, এমন আরো কিছু ছবি বানান।",0,entertainment
কবে প্রতীক্ষার অবসান হবে।কবে দেখতে পাব প্রিয় মুখ গুলো একসাথে।,0,entertainment
"মনোবিজ্ঞানী সিগমুন্ড ফ্রয়েড ও লালন একই কথা বলেছেন।<br /><br />এই মুভিতে লালন,তার সারাটি জীবন ধরে &quot;মনের মানুষ&quot; খুজে গেছে। <br /><br />&quot;মনের মানুষ&quot; কথাটার মানে হলো, আমাদের মনের সাব-কনশাস মাইন্ড এরসর্বোচ্চ উচ্চ পর্যায়।যে পর্যায় প্রচুর জ্ঞানের অধিকারী। <br /><br />যারা আরো বিস্তারিত জানতে চান, তাদের জন্য একটা রাস্তা বলে দেই। <br /> <br />আপনারা সিগমুন্ড ফ্রয়েডের বই পড়ুন।",0,entertainment
সফি কফি শপ। কেরানিগঞ্জের আটিবাজার। থেকে একটু দূরে এলাকার নাম গুইটা ।,0,entertainment
এই রকম গান আর হয় না,0,entertainment
আরো নষ্ট ছবি দেখব ছবি,0,entertainment
আপনি চিকন নাকি মটা আগে সেটা বলেন,0,entertainment
অনেক অনেক সুন্দর মুভি দেখে ভালো লাগলো,0,entertainment
তুমি আমাকে ভুলে গেছো,0,entertainment
ফুল বাজে মুভি,0,entertainment
নাটোক টা খুবি সুন্দর,0,entertainment
ভারত ও বাংলাদেশে রাজনীতি ও দুর্নীতিতে দেশ শেষ। জী আমি ভারতের পশ্চিমবঙ্গ রাজ্যের মালদা জেলা থেকে দেখছি। বাস্তবে এসব হয় ও হচ্ছে।,0,entertainment
অনেক অপেক্ষার পর টা পাইলাম।,0,entertainment
হিরো আলম ফেল নায়কের কাছে,0,entertainment
মডেল আর খুজেপান নাই,0,entertainment
অনেক বেশি ফালতু নাটক,0,entertainment
এটা সিনেমা হলেও এমন বাস্তব ও এমন প্রতিবাদ করার মতো ইচ্ছা বাস্তবেও অনেক লোকের মধ্যে আছে কিন্তু উপায় নেই কারণ একজন বিচারক নিজের চাকরির জন্য অশিক্ষিত নেতার কাছে সুপারিস করার জন্য পা টিপতে হয় সেই দেশে নিতি নিয়ে বাচাটা অসম্ভব,0,entertainment
আমার অসম্ভব প্রিয় একটা মুভি💜💜,0,entertainment
এত বাজে ব্যাবহার চি চি চি,0,entertainment
পরিচিত কন্ঠ,0,entertainment
জান্নাতের মুখে হাসি দেখলে অনেক ভালো লাগে,0,entertainment
ভাই আরো সেক্সী মুভি দেন না হলে রাখ করবো,0,entertainment
আসলেই প্রসংসা না করে পারছি না পরিচালকের।,0,entertainment
এই সব দালালের বিরুদ্ধে সরকার একশান নেই না কেনো?,0,entertainment
এত ভাল লাগে কেরে বুঝিনা,0,entertainment
"নস্টালাজিক হয়ে ছোট বেলায় এই মুভির টিম টোন শুনে কান্না করে দিতাম কারন আমার বাবারসরকারি চাকুরি ছিল ,আমার ও দিপুর মতইবন্ধু হারাত , আর আমি ১৯৯৬ সালে ১ম স্কুলে ভর্তি হই ।",0,entertainment
নায়ক খুজে পাইলো না আর,0,entertainment
সত্যিই দারুণ ছিলো? ভালো লাগালো।,0,entertainment
এর শেষ পর্যন্ত দেখতে চাই// দয়াকরে তারাতারি ভিডিও বানান ভাই প্লিজ????????,0,entertainment
আসলে অনেক পাইন হইছে বিসেশ কড়ে<br />আখম ভাই অসাদরণ<br />রাজ সৌইডি পবাশি +৯৬৬৫৭২৩৪০৩০৮,0,entertainment
এটা কেমন গান ভাই <br />এগুলো পাব্লিশ করে কে <br />ইকটু ভেবে করেন আমাদের তো <br />ভালো লাগার ভালোসার দরকার আছে,0,entertainment
বিচারক গুলারে জুতা পিঠা করা দরকার ।,0,entertainment
আমরা ফেরাঊন ও আবু জাহেল কে নিয়েও সমালোচনা করি তাই বলে তারা কি বড় কেউ নাকি,0,entertainment
"নাটক টা অনেক সুন্দর ভাই, এমন একটা নাটকের কাজ করতে পারলে, অনেক ভালো হতো ভাই।",0,entertainment
এমনটা যেন কারো সাথে না হয়।,0,entertainment
চরম ভাল লাগল গল্পটি,0,entertainment
ফাটা ফাটি হইছে বস।এক কথাই অসাধারণ একটা গান।,0,entertainment
"আর যেই মহিলা কোরআনের হাফেজ,,, আমার মা ও কোরআনের হাফেজ আমি সেই মহিলাকে কিনতে চাই,, কত টাকা লাগবে বলেন,, আমি দুবো",0,entertainment
অনেক পুরনো সুন্দর একটি ছবি,0,entertainment
দিলদার নাসরিন জুটি অসাম কমেডি হইতো,0,entertainment
আর মানুষের মধ্য থেকে কেউ কেউ না জেনে আল্লাহর পথ থেকে মানুষকে বিভ্রান্ত করার জন্য বেহুদা কথা খরিদ করে আর তারা ঐগুলোকে হাসি ঠাট্টা হিসেবে গ্রহণ করে; তাদের জন্য রয়েছে লাঞ্ছনাকর আযাব সূরা লোকমান নং আয়াত তারপর যারা মন্দ কাজ করেছিল তাদের পরিণাম মন্দ হয়েছিল। কারণ তারা আল্লাহর আয়াতগুলোকে অস্বীকার করেছিল এবং সেগুলো নিয়ে ঠাট্টা বিদ্রূপ করত সূরা রুম নং আয়াত,0,entertainment
"ভাই দেখা ছবি দেন কেন এই ছবি অনেক বার দেখেছি যদি পারেন তাহলে রুবেলের,,,<br /> জজ সাহেব, পলাতক আসামী, পেমিক ডাকাত, ইনকিলাব ,নিশ পতি, বিচারপতি ,গোয়েন্দা, লড়াকু সন্তান ,ও শাবানাওআলমগীরে,,,,<br /> বাংলার বধু ,বাপের টাকা ,গরীবে বউ ,শাস্তি চাই ,এই ছবি গুলো যে কোন একটা ছবি দেন ভাই আপনাদে কাছে আমার অনুরুদ",0,entertainment
আমার কাজে ছবিটা অনেক অনেক ভাল লাগে &quot; সাকিব ও অপু আমার কাজে ভাল,0,entertainment
আমি ওরে ভাড়া নিব প্লিজ ভাই আপনি কিছু করে দেন টাকা পয়সার ব্যাপার না। প্লিজ সপ্ন ভাই,0,entertainment
এমন বড় মনের স্বামিদের জন্য আমারআন্তরিক অভিনন্দন।,0,entertainment
বুঝিনা ছবিতে গানগুলো থাকেনা কেনো?,0,entertainment
সাইমন আসলেই অভিনয় জানে,0,entertainment
মেয়েরা চায় তারা এগুলো করে বেড়াক আর স্বামী মেনে নিক।কমেন্ট পড়ার পরে এমন মনে হলো।,0,entertainment
খুবই সুন্দর প্রেমের গল্প,0,entertainment
দুধ গুলো বের কর।মাল অাউট করি,0,entertainment
"সত্যি কথা বলতে যারা সিনেমাটি বানিয়েছে, তারা চেষ্টা করেছে কিছু একটা করার",0,entertainment
বাংলার বাঘ মুভি ভাল হয়েছে,0,entertainment
গরীবের ক্যাটরিনা কাপুর চুপুর,0,entertainment
"আগেরদিন গুলোর ছবি দেখলেই ছুখে পানির বন্না বয়ে যেত আর এখন ত ঘৃনা লাগে ছবি দেখলে,,ভাল কাটুক সবার জিবন",0,entertainment
আসুন সবাইকে নিয়ে পাচ ওয়াক্ত নামাজ পরি।,0,entertainment
শাকিব খান এর নোলক মুভির গান দেউ,0,entertainment
কত তারিখ আসবে..... আর গানে নিশো ভাই কই❤❤❤I LOVE,0,entertainment
ভালোবাসা গুলা মনে হয় এমনি হয়।,0,entertainment
আমার তো এখানের যে কয়টা স বাই পাগল এদের কে আগে পাভনা পাটানো দরকার,0,entertainment
নাইস হিস্টুরি,0,entertainment
কান্না করে দিলাম 😢😢,0,entertainment
ফাহমি কে আপনি চিনেন,0,entertainment
সবাইকে আমার প্রোফাইল থেকে ঘুরে আসার দাওয়াত রইলো,0,entertainment
আমার অনেক পছন্দের মুভি আমি অনেক বার দেখছি।,0,entertainment
আমি জান্নাতে 155 পর্ব দেখে বসে আছি দুঃখের বিষয় হলেও মনে হয় এটা কপিরাইটের জন্য আমাদের দেশে বন্ধ করে দেয়া হয়েছে কিন্তু তারপরও কষ্ট করে ভিপিএন দিয়ে জান্নাতের ফাইনাল পর্বদেখছি তুর্কি ভাষায় খুব ভালো লাগলো শেষ করবে জান্নাত আর সেলিমের বিয়ে হয়খাইয়া মারা যায় সবাই আমার চ্যানেলটি সাবস্ক্রাইব করবেন প্লিজ,0,entertainment
"আমাদের এখানে এমন গলি আছে,রাতের গলি",0,entertainment
এই মুভি দেখলে চোখের পানি কে আটকাতে পারে,0,entertainment
কি ভাই এরা কি কখনো বিচারক হয়েছিল মনে হয়তো না এটা এমনই একটা জায়গা এখানে আসলে মানুষ এমনি তো নার্ভাস হয় ভালো বলতে হবে তাদেরকে সাহস দিতে হবে না তুমি পারবা আর একটু প্র্যাকটিস করো এভাবে তাহলে হয় তাই না তা না বলে কি করছো একটা জীবনে পড়ছো এটা জানো আরে ভাই জানলে কেন তোমাদের মতন তো টিচের হয়ে যেত।,0,entertainment
সিনেমা হলে গিয়া দেখেছিলাম ৮ টাকা দিয়ে😀😀😀😀,0,entertainment
অনেক ধন্যবাদ সবাইকে কষ্ট,0,entertainment
চোখের পানি ধরে রাখতে পারলাম না একটা ছেলে সবকিছু ত্যাগ করে প্রবাসে থাকে,0,entertainment
বাংলা মুভির পোষ্টার দিবেন,0,entertainment
ভাই নাটক টা অনেক সুন্দর,0,entertainment
গানটা এত হিট হয়েছে ঘণ্টার মধ্যে লাখ বিশ হয়েছে হাজার লাইক কমেন্ট করা হয়ে গেছে এত সুপারহিট গান শাকিব খান নুসরাত ফারিয়া আশা করি এক সপ্তার মধ্যে মিলিয়ন ভিউ হবে যিনারা শাকিব খান কে ভালোবাসেন অবশ্যই একটা লাইক হিট করবেন গানটা শুধু দেখতে ইচ্ছা করে বারের উপরে দেখে ফেলেছি এত ভালো লেগেছে সুপারহিট শাহিন শা,0,entertainment
জোউতুক ছাড়া বিয়ে।সোকল পরিবারের হক,0,entertainment
বয়ঃসন্ধিকালের ম্যাচুরিটি।।।😍,0,entertainment
ওওওমা আমি তোমাকে অনেক ভালোবাসি মা।মা তো মাই মায়ের সাথে কারও তুলনা হয়না।অনেক মিস করি তোমায় প্রবাসী ছেলে তোমার।😥😥😥😥,0,entertainment
এই ছবিটা আমার খুব পছন্দের ছবি <br />এই ছবির গান গুলাও খুব সুন্দর লাগে,0,entertainment
এই গল্পগুলো হুমায়ুন আহমেদ ছাড়া কাউকে দিয়েই সম্ভব না। অনলি হুমায়ুন আহমেদ ইজ রিয়েল। 💝,0,entertainment
ইদানিং ইউটিউব এ একটা দেখছি তারকিশ সিরিয়াল - প্যায়ার লাফজো মে কাহা। খুব ভাল লাগছে,0,entertainment
আমার গরম লাগছে কেউ কি আছ লাগানো জন্য আমারসঙ্গে করতে হলে চেনেলে আসুন,0,entertainment
আমি মনে করি জে এই মন পুরা ছবি টা জে পরি চালক সেজেন এরকম ছবি আর না করে তাহলে আমাদের মত ছেলেরা মারা জাভে খুব কষ্ট হয় এরকম ছবি দেখলে,0,entertainment
আপনাদের কাছে কোন নিউজ না থাকলে বসে বসে স্টুডিওতে মশা মারেন তারপরে এরকম আবাল মার্কা নিউজ কইরেন না।,0,entertainment
অভিনয়ের মারে বাপ করে দিছে,0,entertainment
"অনেক অনেক ধন্যবাদ শ্রদ্ধেয় কাজী হায়াৎ স্যারকে,,,মান্না ভাইকেএই সুন্দর অভিনয় করানোর জন্য,। সালাম দুজনকেই।",0,entertainment
এখানে ফেরদৌসের দোষ ছিলো সে জুয়া কে বেশী গুরুত্ব দিয়েছিলো কিন্তু অমিত হাসান জুয়ায় জিতার পর মানবতার জন্যে হলেও ফেরদৌস কে বউ ফেরত দেওয়া উচিৎ ছিলো। যাই হউক ভূল থেকেই মানুষের শিক্ষা নেওয়া উচিৎ।,0,entertainment
সানাই প্রথমে পরিচালককে মজা দেয় তারপর ফিল্মে চান্স পায় আর সে যদি পরিচালকের চাহিদা পূরণ না করত কখনো ফিল্মে চান্স পাইতোনা,0,entertainment
"খুব ভাল, লাগল,",0,entertainment
প্রাথমিকভাবে হলেও এগুলো কেমন করে বিচারকের জায়গায় বিলং করে ! তাদের ব্যবহার ই কোনভাবে জাজমেন্ট এর পর্যায়ে পড়েনা।বি গ্রো ম্যান মোস্তফা কামাল রাজ ছাড়া অন্য রা এ জায়গায় আসে কেমন করে,0,entertainment
পাগল ছাগল দাড়িওয়াল কই বাড়ি পাবনা পাঠান,0,entertainment
পাগলের অভিনয় ভাল লাগে,0,entertainment
এক নাম্বার ছাগল,0,entertainment
বেশি করে পুরনো সিনেমা চাই। ওগুলো বাংলার সম্পদ। দেখলেই মন ভাল হয়ে যায়। আগের স্মৃতি মনে পড়ে যায়। তবে ছবিটা অচল পয়সা ছবিটার সাথে মিলে গেল।,0,entertainment
এইটা সোনার নাটক,0,entertainment
আবার যদি আগের মতো রিয়াজ শাবনুর এই রকম মুভি বানাতো তাহলে বাংলার মানুষ আবারও সিনেমা হলে গিয়ে মুভি দেখতো আমি প্রেমের ছবি দেখলে একমাএ রিয়াজ শাবনুর পুর্নিমার ছবি দেখি আর মারা মারির ছবি দেখলে মান্নার মুভি আর তাও যদি দুই একটা দেখি জসিমের মুভি দেখি আর না হলে বাংলার কোনো নায়ক কিবা নায়িকার ছবি আর দেখি না আর মান্না মারা যাওয়ার পর বাংলা মুভি দেখা বন্ধ করে দিয়েছি আর কোনো দিন বাংলা মুভি দেখবোনা আর এখনো যদি দুই একটা দেখি তাহলে পুরনো মুভি গুলো দেখি,0,entertainment
"কান্না ধরে রাকতে পারলাম না, সত্যিই খোব দুঃখ্য জনক বিষয়, কেউ টাকা রাখার যায়গা পায় না,(অপব্যায় করে)আর কেউ একটি টাকার জন্য মানুষের ধারে ধরে ঘুড়ে,,,",0,entertainment
যদি পারেন মানুষের উপকার করেন ক্ষতি করবেন না। আপনি যদি মানুষের এক টাকা ক্ষতি করেন তাহলে আপনার আরো বেশি ক্ষতি হয়ে যাবে।নামাজ কায়েম করুন। হালাল পথে ইনকাম করুন। কারো ক্ষতি করবেন না। মানুষের উপকার করবেন তাহলে দুনিয়াতে এবং আখেরাতে শান্তি পাবেন।মানুষকে ক্ষমা করতে শিখুন তাহলে মনে শান্তি পাবেন। মানুষের সাথে ভাল ব্যবহার করুন।,0,entertainment
কি সুন্দর মুবি মান্না ভাইর কিং খানের রাজা,0,entertainment
আগুন লাগিয়ে দিছে,0,entertainment
টাকার দরকার হলে তোর বউরে বাজারে নামায় দে---,0,entertainment
হুজুরের পাট ভালো লাগছে,0,entertainment
কাবলি ওয়ালা অসাধারণ হল মুবিটি,0,entertainment
তুমাকে বলও লাগে কিনতু তুমার একটা সমওসা তারাতারি পেমে ওরে জাউ,0,entertainment
দোয়া করি এরা যেন ভাল হয়ে যাই,0,entertainment
বাংলাদেশ আজ এইসব দালালদের জন্য নেয়বিচার পাই না,0,entertainment
শিল্পা সিন্ডা কে পর্ণ তারকা নাকি,0,entertainment
অনেক দিন পরে দেখলাম তার পরও খুশি,0,entertainment
এই নাটক গুলো আস্তে দেরি হয় কেন,0,entertainment
মম এর দুদুর দিকে তোমার কু নজর কেন,0,entertainment
পারলাম না দরে রাখতে ছোখের পানি,0,entertainment
"ফ্লপ মুভি গ্যারান্টি১০০%<br />স্ক্রিনশট নিয়ে রাখেন,, <br />সবার অভিনয় ভালো হবে শুধু মাহির সাথে নায়কের পালতু লুক টা মুভিটা খেয়ে দিবে।",0,entertainment
আবলা আবলা আবলা,0,entertainment
"নাটকটি অসাধারন।কিন্তু একটি ব্যাপার ভিন্ন দেশের কোনো নাটক বা সিনেমাতে আমরা দেখি চরিএ নিখুত ভাবে ফুটিয়ে তোলার জন্য প্রয়োজনে সত্যিকারের মাথা ন্যাড়া,দাড়ি রাখা,চুল বড় রাখা ইত্যাদি অভিনেতাদের করতে দেখা যায়।আর আমাদের দেশে বিশিষ্ট কথা সাহিত্যিক হুমায়ুন আহমেদের সৃষ্ট হিমু চরিএে মোশাররফ করিমের মেকাম,কস্টিউম অত্যন্ত বেমানান।নকল দাড়ি বাতাসে উড়ছে,দাড়িও এত বড় দেখানোর প্রয়োজন ছিলো না,একহাত ঢোলা পায়জামা,চুল চরমমাএায় অগোছালো।হিমুর প্রকৃত চরিএ একটু এলোমেলো ধরনের,অগোছালো না।মোশাররফ করিম সাহেবের উচিত ছিলো দুই মাস সত্যিকারের দাড়ি রেখে নাটকটি করা।তাহলে এত আবেগ ও বিনোদনময় হিমু চরিএটি রুপদান সার্থক হতো।",0,entertainment
খুব সুন্দর লাগে,0,entertainment
"এ কাল সে কাল মিলিয়ে সর্বো স্রেষ্ঠ ও চির সবুজ অমর অভিনেতা সালমান শাহ, আল্লাহ তাকে জান্নাত দান করুন,",0,entertainment
অনেক দিন যাবত ছবিটা খুজতেছিলাম অবশেষে পেয়ে গেলাম। আপনাদের ধন্যবাদ ছবিটা দেওয়ার জন্য।,0,entertainment
মানুষ সবকিছু ঠিকঠাক নিয়ন্ত্রণ করতে পারে শুধুমাত্র এটি নয় সাগরের জলে বিশাল জাহাজ কে ও নিয়ন্ত্রণ করা যায় কিন্তু ঘরের নারীকে নিয়ন্ত্রণ করা যায় না ইহা একটি অনিয়ন্ত্রিত জলোচ্ছ্বাস কাল বৈশাখী ঝড়ে মতো তাহার নাম ঘরের বউ ।<br />সবকিছুই বুঝিয়ে আসা যায় কিন্তু ঘরের নারীকে বুঝানো যায় না.!,0,entertainment
"বাংলাদেশ কারিগরী শিক্ষা বোর্ড এর অধীনে ৬ মাস মেয়াদী কম্পিউটার সার্টিফিকেট কোর্সে ভর্তি চলছে...।<br /><br /><br /><br />আপনি এখন রেজিস্ট্রেশন সম্পন্ন না করলে পিছিয়ে যাবেন ৬ মাস, তাই দেরি না করে আজই আপনার রেজিস্ট্রেশনটি সম্পন্ন করতে চলে আসেন বাংলাদেশ কারিগরি কম্পিউটার একাডেমি তে।<br /><br /><br /><br />আমাদের ঠিকানাঃ<br /><br /><br /><br />যোগাযোগ করুনঃ বাংলাদেশ কারিগরি কম্পিউটার একাডেমি , পরিচালক মো: আরিফুল ইসলাম বানেশ্বর বাজার (N.C.C BANK) ভবন মোবাইলঃ ০১৭৭৭৫৩৬০৫৯",0,entertainment
পোতি নাটোকে মোসারোফ কোরিম কেনো তার বউ কে নেই দেখলেই মেজায খারাপ হইয়া জাই। পেতনিরে কেনো নাটোকে নেই ভালো লাগেনা। আরো নাটোকের মুড নোসটো কোরে দেই,0,entertainment
সিরিজ দেখার নেশা আর গেলো না।এক বসাতে সব ফালিয়ে সিরিজ দেখার নেশায় ডুবে যাই।আজ দেখা শুরু করলাম। সারাদিন এ ৩০ টা দেখে শেষ করলাম। পরের বসাতে বাকি গুলা দেখে শেষ করবো।,0,entertainment
শাবনূরের মত আমার প্রেমিকা,0,entertainment
তারা তো গালিরও যোগ্যতা নেই কারন গালি দেয়ার মতো গ্যোতা লাগে ঃ তারা শুধু ফ্লাই ওভারের যোগ্যাতা অর্যন করেছে যাতে তাদের উপর পায়ে জোতা নিয়ে ওই ফ্লাইওভার দিয়ে বাংলার সব ছেলেরা হেটে যাওয়া যায়,0,entertainment
একটা নষ্ট হাজারও ভালবাসায় কষ্ট দিতে পারে।,0,entertainment
শাকিব ভক্তরা কই সারা দেও ।,0,entertainment
"আল্লাহ তুমি মহান! তুমি এই পৃথিবীর মালিক! আল্লাহ তুমি সালমান শাহ এর এত জনপ্রিয়তা আর এত মানুষ এর দোয়ার পরিবর্তে তুমি তার সারাজীবন এর সকল গুনাহ মাফ করে দাউ,,,, আমিন!। সবাই আমিন বলেন.।।",0,entertainment
দেখে খুব ভালো লাগলো,0,entertainment
"কথাটা খুব বলতে ইচ্ছে করে, লাভ অফ মাই লাইফ!!",0,entertainment
পৃথিবীতে সবচেয়ে গুরুত্বপূর্ণ হলো মায়ের ভালোবাসা মাকে কখনো কষ্ট দিওনা pls pls,0,entertainment
"আমাদের সমাজি কিছু নর পিচাশ পুরুষদের কারণে মেয়েদের খারাপ পথে যেতে হয়, ধিক্কার জানাই সেই সব পুরুষদের যারা বিয়ে করে বউকে আগলে রাখতে পারে না!!!!",0,entertainment
ফাটাফাটি একটা নাটক দেখলাম,0,entertainment
বাংলাদেশ থেকে কোনোভাবেই মানব পাচার বন্ধ করা যাচ্ছে না | বরং পাচারকারীরা নানা কৌশলে প্রতিদিনই দেশ থেকে মানব পাচার করে যাচ্ছে | আইনে মানব পাচারের সর্বোচ্চ শাস্তি মৃত্যুদন্ডের বিধান রাখা হলেও পাচারকারীরা এর তোয়াক্কা করছে না | <br />তাহলে উপায়......( আপনার উত্তরের অপেক্ষায় থাকলাম),0,entertainment
"আচ্ছা এই ছবির নায়িকার পুরো নাম কি? ছবিতে Only বৃষ্টি দেয়া আছে, উনি কি বেচেঁ আছে? যদি বেচেঁ থাকে কি অবস্থা?",0,entertainment
মাইয়ারা জেইডা করে অইটাই ভালো। আর ছেলেরা করলে খারাপ ?।এই হচ্ছে শেখ হাসিনার বাংলাদেশ,0,entertainment
"রিয়াজ,পূর্ণিমা,শাবনুর বাংলা ছবির অনেক বড় সম্পদ❤",0,entertainment
তোর মাইরে বাপ,0,entertainment
জটিল,0,entertainment
"প্রত্যেকটা বাবা মা&#39;র উচিত বিশ বছর বয়স হলে ছেলে মেয়েদের বিয়ে দেয়া হয়ত বলবেন খাওয়াবে কি, আমি বলব আপনার বিয়ের পর থেকে ছেলে মেয়ের বিয়ে পর্যন্ত এই লম্ভা সময়টাতে আপনি কি করেছেন যে ছেলেকে নিজের পায়ে দাড়াতে হবে, আর এমনিতে বিয়ের পর সবাই কর্মজীবি হয়ে যায়, বিয়েটাকে সহজ করে দিন বাবা মায়ের প্রতি আমার অনুরোধ",0,entertainment
টাকা থাকলে কিনা করা যায় তা আবার ও প্রমান হয়ে গেলে,0,entertainment
মাহি তুমি আমার পছন্দের নায়িকা কিন্তু তুমি এমন কিসব নায়কের সাথে ছবি করো। ভাল নায়কের সাথে ছবি করো প্লিজ,0,entertainment
অনেক দিন পর মুভি টা পেলাম,0,entertainment
এই ঘর এই সংসার বাস্তবের সাথে মিল আছে,0,entertainment
লিজার আরও মুভির নাম কেউ বলবেন প্লিজ,0,entertainment
এই ধরনের ভিডিও আর বানাবেন না,0,entertainment
জাকিয়া বারী মমের নাটক দেখব না কমেন্ট করার জন্য আয়ছি,0,entertainment
বাকি সব কবে দিবেন। তারাতারি দিবেন প্লিজ,0,entertainment
এতো নোংরা বিচারক আমাদের দেশেই হওয়া সম্ভব,0,entertainment
"এক মুভি কয়বার কয় চ্যালেনে ছাড়ে??<br />এইটা এর আগে ইউটিউব এ অনেকেই <br />ছারছে,,,",0,entertainment
এই জন‍্য বলে বরিশালে খেয়াল গাট্টি,0,entertainment
দেশে যে হারে নকল দুধ আসা শুর করছে জাক পাবলিক বিনা পয়সায় দুধ পাবে খাটি দুধ পাবে।,0,entertainment
এরকম ছবি আরো দরকার বর্তমানে কিন্তু এখনকার পরিচালকরা এসব ছবির কথা ভাবেও না,0,entertainment
এই সিনেমার সকল গান চাই.....প্লিজ দিবেন.....,0,entertainment
পার্থিব ভাই আপনি এই এপিসোড গুলাকে ধীরে ধীরে একটা বাস্তবচিত্রে প্রবাহিত করুন।প্রয়োজনে অন্যের সাহায্য নিন। like as a prostitute.,0,entertainment
ভালোবাসি ভালোবাসি তোমাকে এই গানটা দিয়ান,0,entertainment
আসলে কি বলবো আগের মতো ছবি এখন আর বাংলাদেশে নেই।,0,entertainment
"অনেক মিস করি মহা নায়ক মান্না ভাই কে দোয়া করি মহান আল্লাহ যেন ওনাকে মাফ করে দেন,",0,entertainment
বস্তাবন্দ নাটক আর নষ্ট গল্প দিয়া চলে,0,entertainment
নেই যখন তখন এসব বোকার মত video করেন কেন? আর সত্যিই কোন কাজ নেই আপনাদের! নাহলে বলেন যে এটা একটা জাতীয় সমস্যা/ খবর !!!!! আর বাংলা দেশের মেয়ে দের নিয়ে অত চিন্তা না করলেও চলবে আপনার কেননা তারা যথেষ্ট বুদ্ধিমতী ও তাদের হীন ভাবার অধিকার কেউ আপনাকে দেয় নি। বিকৃত মানসিকতা নিয়ে কিভাবে বাঁচেন!?!?,0,entertainment
পকিন্নির বাচ্চা,0,entertainment
এই শাকিব খানের ছবিটা আমি কতবার দেখছি জানিনা এত কষ্টের ছবি ছবিটা দেখে আমার অনেক কষ্ট লাগছিল,0,entertainment
"বিজলী মেয়েটা বলে কি,,..? টাস্কি খাইলাম",0,entertainment
আজকের সমাজের কিছু কিছু নর পষু আর কিস্তি দুইটাই খারাপ ওদের কাছ থেকে বিরত থাকা ভাল আর আমি মনে করি কিছুটা বাস্তব চিত্র কারন কিস্তি ঘরে জদি লাশ তাকে তাহলে ক্ষমা নাই দেওয়া লাগবে,0,entertainment
কে হবে মাসুদ রানাকে নিয়ে যতোগুলা রোস্ট ভিডিও দেখেছি আপনার রোস্ট ই সেরা আর্টিসদের সাথে বাজে আচরণ ভুল এবং চোখে আঙ্গুল দিয়ে দেখিয়ে দিয়েছেন! আপনার ফ্যান হয়ে গেলাম তাহসিনেশান ভাই🌸❤,0,entertainment
ভাই থামেন থামেন কিভাবে ভরলেন এত স্ট্যমিনা,0,entertainment
এই ছাগল এর বাচ্চাদের নাটক কেন যে মানুষ দেখে,0,entertainment
"তানজিন তিশাকে,,,আফ্রান নিশুর সাথে মানায়",0,entertainment
আলেকজান্ডার বো এর ছবি মানেই কাহিনী ও এ্যাকশন। আলেকজান্ডারের বো অভিনীত মুভি অনেক ভালো লাগে৷,0,entertainment
এটা জনগণকে বিচ্ছেদে আরো উৎসাহিত করবে । এটা মোটেই কাম্য ছিলো না। আমার দেখা ওয়ান অফ দ্য বেস্ট কাপল ছিলো তারা। আই উইল জাস্ট মিস দেম,0,entertainment
অনেক পছন্দের একটি সিনেমা।<br />আলমগীর-শাবানার অভিনয়ের তুলনা হয়না।,0,entertainment
ফালতু মুভি অশ্লীল সাকিব আগে করত,0,entertainment
আমি নাই বলে আমার বউকে তুই দর্শন করস আজ তোর একদিন আমার যতদিন লাগে,0,entertainment
আগেরচবি গুলোঅনেকসুন্দরচিল।<br />এখনকার ছবিতেহিট হয়না।,0,entertainment
আমার বোর্ড আমার বেলোট বক্সে_ বরতো মানে আমি ইনটারন্যাশনাল_ আমি এখন নয়ে লকাল,0,entertainment
কোথায় থেকে পাগল ছাগল ধরে এনে নাটক বানিয়েছে,0,entertainment
ফারিয়া মমোদের ফ্যান পেজে করতে থাকেন,0,entertainment
"কালের বিবর্তনে এই মুভি আজ বিলুপ্ত প্রায়। <br />হয়তো আর আর দেখা যাবে না সেই সোনালী দিনের বর্ণালী বাংলা সিনেমা। <br />হয়তোআর দেখতে পারবেন না সেই চন্ঞ্চল ও মিলিরজুটি। <br />বাংলা চলচিএের প্রান বলা হতো ওদের। <br />বাংলা চলচিএে ওরা এক নতুন অধ্যায় খুলে গেছে। <br />২০ শতকের শ্রেষ্ট অভিনেতা ও অভিনেএী। <br />বাংলা চলচিএে এক সময় তারা শাসন করে গেছে। <br /><br /><br />হয়তো আর ফিরে আসবে না সেই সোনালী দিন , শুক্রবার <br />বিটিবি তে শতো বিজ্ঞাপনের মাঝেও সেই চলচিএ গুলো দেখতাম। <br />আধুনিকতার ছোয়ায় তা আজ বিলুপ্ত প্রায়। <br /><br />যদিও আসে তা আমাদের জন্য কেবল সপ্নই বটে। <br />হয়তো আর দেখতে পারবো না , <br />মনপুরা চলচিএের মতো চলচিএ । <br /><br />সাকিব খান দের মতো তরুণ্যদের জন্য , <br />(২০ শতকের প্রথম পর্যায়ে যারা হুংকার দিয়ে জানিয়ে দিয়ে গেছে যে বাংলা চলচিএে একমাএ শাসনকর্তা আমরাই ) ওদের থেকে শিক্ষা গ্রহন করাটাই শ্রেয় হবে। <br /> ফারহানা ও চন্ঞ্চলতাদের মধ্যে একজন । <br />জাতিকে তোমরা অনেক দিয়েছ । <br />জাতির চাওয়ার কিছুর নেই আর। <br /><br />জাতির এখন একটাই চাওয়া যেনো তোমরা সুখে থাকো। <br />বাংলা চলচিএে তোমাদের নাম চির বিরাজমান । <br />জানি না তোমরা বড় বড় অ্যাওয়ার্ডে পুরষ্কার পেয়েছো কিনা। <br />কিন্তুু আমার দুনিয়ায় একমাএ বিচারক আমি নিজেই । <br />তোমাদের ক্ষেএে আমার বিচার করার ক্ষমতা খুবই নগণ্য । <br />তার থেকেও শ্রেষ্ট তোমরা । <br />শুভকামনা রইল যেনো আগামির দিনগুলি সুখেই কাটে ।",0,entertainment
দৌলদিয়া পতিতা পল্লী. আমিসুমন ভাই 01942316324,0,entertainment
তারেকের অভিনয় আনবদ্য ছিল,0,entertainment
ভালোবাসার মানুষ চাই একজন খাটি প্রেমিক চাই যে আমাকে ছেরে যাবেনা কোনদিন❤❤❤❤❤❤❤❤❤❤❤❤❤❤👀👀👀👀💙💙💙💙💙💙💙💙💙💙💙💙💙💙💙💙💙💙💙💙💙💙💙❤❤❤❤❤❤❤❤💙💙💙💙💙❤❤❤❤❤❤❤❤💙💙💋💋💋💋💋,0,entertainment
"প্রতিটি মানুষের একটা ভালো দিক থাকে,,,,,,,,,,,সে যতই খারাপ হোক না কেন?",0,entertainment
"সবার জীবনের সাথে নাটকটা মিলে গেছে, তেইলে আমার টা কই।।। 😉😉<br />সত্যি অনেক সুন্দর নাটক।।।।",0,entertainment
হোস্ট আপু তুমি একটা জিনিস,0,entertainment
আসলে সব দোষ জি বাংলার,0,entertainment
"বোঝাই যায় ফালতু মেকিং, কিন্তু তবুও কেউ যদি এই সিনেমাটা দেখে তবে তা শুধুমাত্র আমিন খান আর মাহির জন্যই!",0,entertainment
জুব সমাজ মনে হয় দিন দিন কেমন জানি হয়ে যাচ্ছে 😂😂😂😂😂,0,entertainment
এইটা শাকিবের নিজেরি বাড়ি,0,entertainment
নাইকা আর খুজে পান নি ভাই,0,entertainment
মির সাব্বির এর নাটক। <br /> অনেক ভালো লাগে।।<br />সে আরো ভালো নাটক আমাদের উপহার দিক।।।,0,entertainment
মরতে হবে এক দিন এটা মনে রেখো আল্লার নাম নিয়ে য়দি কেউ কিছু করে তা হলে আমরা মুসলাম মেনে নিবোনা কথা টা মনে রেখো আল্লাহ আমাদের পতি পালক আমার রহিম রহমান,0,entertainment
"আদৌ কি পাবো না, ভাগ্য বিড়ম্বনা।",0,entertainment
অনেক সুন্দর একটা কাহিনী অনেক কিছু বোঝার আছে ।,0,entertainment
গানটা যতটুকু ভালো কিন্তু ড্রেস টা কি মেয়েটার 😠😠😠,0,entertainment
গায়ক তো এটা সজল 😂😂,0,entertainment
এমন নাটক হওয়া উচিত যা সমাজের জন্য উপকারী ।,0,entertainment
মোশারফ করিম কে আমি ও সবাই ভালো বাসতো কিন্তু ভালো অভিনেতা হলেই সব জানবে এটা ঠিক না। তানা হলে ডক্টর লাইনে পড়ে ইন্জিনিয়ারিং কাজ করা যেতো।তাই বোরকা নিয়ে যে নাস্তিক এর পরিচয় দিয়েছেন তার পর ও নাটক কেউ দেখে না।,0,entertainment
এই ছবিটার নকল করেই বলিউড নামাস্তে লন্ডন ছবি বানিয়ে কোটি কোটি পাউন্ড বাবসা করেছিল। অথচ আমাদের প্রতিভাটাকে ওর মেরে ফেলেছিল,0,entertainment
বন্ধু তুমি আমার শেখ মুস্তাকিম,0,entertainment
পরিচালক পাগল বই টা মিলন ঠিক করতে পারিনি,0,entertainment
বাংলাদেশের হিরোইন হতে হলে হিজড়া হতে হবে। এবং হিরো হতে হলে নপুংসক হতে হয় । তার কারণ যাতে যতই যা কিছু করা হোক না কেন তাতে বাচ্চা হবে না বাচ্চা হবে না বাচ্চা হবে না🤣,0,entertainment
যদিও মুভিটা খুব বাস্তব সম্মত কষ্টের। তবে একটা জায়গায় না হেসে পারলাম না_<i>_</i> তোর মুচের দুই কোনায় ২ টা ইট ঝুলায় দিলে তোর সব মনে পরে যাইবো।😃😃,0,entertainment
ফুল নাটক কই পাবো,0,entertainment
"আসলে < ="": ?_=%%%%%%%%%%"">#জাজ মনে হয় মানুষরে পাগল পাইছে।। ইয়ারা বইলা খাওআইতে চাইতাছে।। এই পুরা গানটা ই বাজে গান।।শুধু একটা কথা পালটাইছে আর মানুষ সবব ভুলে গেছে না??",0,entertainment
ছবিটা দেখে মনটা অনেক খারাপ হয়ে গেল,0,entertainment
"সত্যি যদি প্রেমের আদালত থাকতো,love you Apu.",0,entertainment
চলুন সবাই সবাই কে বন্ধু করে লেটার দিয়ে আসি,0,entertainment
নির্দ্বিধায় বলতে পারি বাংলাদেশের শ্রেষ্ঠ নাটক নির্মাতা হচ্ছে মিজানুর রহমান আরিয়ান ভাই,0,entertainment
দুধ গুলা বেশি বড় না।,0,entertainment
ফারিয়া ফোন দেয়না সারিয়া🤣🤣🤣,0,entertainment
এতো ভালো কেনো রে,0,entertainment
"ধন্যবাদ ,,,<br />অনেক সুন্দর শিক্ষনীয় নাটক।",0,entertainment
মনের জ্বালা মুভি আপলোড দেন প্লিজ HD,0,entertainment
"মনটা জুরিয়ে গেলো,আহ কি গান!",0,entertainment
দারুণ লাগল নাটকটা.....,0,entertainment
জয় একটা পাগল,0,entertainment
আমার জিবনের সেরামুভি,0,entertainment
পুরনো নাটক নতুন বলে চালিয়ে দেয়া হলো বাট আমি মোশারফ ভক্ত বার বার দেখবো,0,entertainment
হাগার হাগার এটা কী ভাই 😂😂,0,entertainment
ফালতু সারমর্ম হীন নাটক।সময়ের অপচয় মাত্র,0,entertainment
আমি অপূর্ব বের নাটক অনেক পছন্দ করি,0,entertainment
ছবিটা দেখে মনের অজান্তেই চোখ দিয়ে পানি ঝরে পরলো😢আসাধরন ছবি।,0,entertainment
একটা গল্প মনে পড়ে গেল একটা বিশাল হাতি মরে পড়ে আছে টা কুকুর হাতির মাংস খাচ্ছে একটা কুকুর আরেকটা কে কামড়াচ্ছে ঝগড়া করতে ছে একা খাবে বলে আপনারাই বলে দুইটা কুকুর যদি মিলে মিশে মাংস খায় তবুও কি মাংস শেষ হবে দেশের হল এই অবস্থা আমার ছোট্র চ্যানেল টি সার্চক্রাইব করার অনুরোধ রইলো সবার পতি,0,entertainment
আরেকটু ভালো খেলনা পিস্তল হয়তো পাওয়া যেত।,0,entertainment
খোব ভালো নাটকদেখে খোব ভালো লাগলো,0,entertainment
সাজ্জাদ যদি ফাহামির সামনে পরতো তাহলে প্রথমই বাদ পরতো।,0,entertainment
সবায় এই চ্যালেন কে আনসাস্ক্রাইব করো এমবি ও খাই টাকাও খাই।তারা অনেক বেশি খুদার্থ। ৫টাকা দিয়ে একদিন কিনলাম তাও এমবি কাটে এপ ডাউনলোড করলাম রেজিস্ট্রার করলাম তাও অধিক পরিমানে এমবি কাটে দূর বাল যত্যসব আজাইরা পাবলিক। ফালতু😡😡😡😡শুধু মাত্র জান্নাত দেখার জন্য এতো কিছু করলাম,0,entertainment
মমর টা একটু বেশি,0,entertainment
বাপের টাকা মুভি চাই,0,entertainment
না বলা কথাগুলো দেখলে বলা হয়ে যায় <br />হাজারো এলোমেলো চিন্তারা আজ ধমকে দাঁড়ায়<br />কেন রে দুচোখে আসেনা ঘুম পলকে আদুরে চুপ। <br />জানিনা হয় রে কেন আমার এমন। <br />মন খুঁজে মন<br />মনের মতো মন❤❤❤❤,0,entertainment
অনেক ভাল্লাগলো,0,entertainment
তাহাসান আমার বস,0,entertainment
আমার ও মন চাইছে ফাহমি ভাই এর দুদ ধরে টিপ দিতে 😂😂,0,entertainment
খুব সুন্দর একটা মুভি।<br />কে কে দেখেছো লাইক হবে??,0,entertainment
কোথায় থেকে এসব পাগল ছাগল আসে,0,entertainment
"সানি ভাইয়ের কুলি ছবি হেবিব,,,,",0,entertainment
পুরুষ এমন এক জাত যে অনেকসময় বোঝেনা আবার অনেক সময় বুঝতে চায়না আবার অনেক সময় বুঝেও মানতে চায়না ছেলে মাতাল হোক খারাপ হোক হোক সমাজ তাকে সহজে মানে তার পাওয়া খুব কঠিন হয়না আর জরিপ করলে দেখা যাবে একটা মেয়ে যতটা করে সংসার চালাতে চায় একটা পুরুষ তা ভাবতে ও চায়না তবু ও অনেক পুরুষ এমন নয় তারা বউ খারাপ হলে ও সংসার করে তাকে করে না থাকলেও বউ এর সাথে সংসার করে তাদেরকে জানাই এ যুগে বউকে দেয়ার,0,entertainment
শাবনুর বলে কথা,0,entertainment
"এই নাটকটি আসলেই অসাধারন হয়েছে , এই নাটকটি বাস্তবতার সাথে মিল রেখে বানানো হয়েছে ।এই নাটকটিতে শেখার ও বোঝার অনেক কিছু আছে যদি কেহ শেখার মতো শেখে ও বোঝার মতো বোঝে ।ধন্যবাদ পরিচালকে ও অভিনেতা জাহিদ হাসান ভাই আপনাকে ।।",0,entertainment
প্লিজ এডমিন ভাই এই মুভির গান গুলো আপলোড দিবেন?,0,entertainment
ভাইয়া রাণীর নাম্বার টা দিবেন প্লিজ ভাইয়া দেন,0,entertainment
অনেক বন্ধু নাটকের নাম যান্তে চাইছে মুন ময়,0,entertainment
সব এপিসোড কেমনে দেখব ভাইয়া??,0,entertainment
পরিচালক কি আর কোনো নায়ক পেয়েছিলো না।।। বাংলাদেশে কি নায়কের অভাব পড়েছিলো।।,0,entertainment
অনেক এক সুন্দর ছবি উপহার দেওযার জন্য ধন্যবাদ ৷,0,entertainment
মাহিয়া মাহির মেকআপ দেখে মনে হচ্ছে। বিগো লাইভে এসেছে,0,entertainment
অপুকে দিলে অনেক ভালো হতো,0,entertainment
"এই চবি অনেক খোজাখোচি করচিলাম,,",0,entertainment
‌কোন ক্লা‌সে প‌ড়ে!,0,entertainment
"এই ছবি দেইখা মনে হইলো এরশাদ শিকদার একটা ভালো মানুষ ছিলো।<br />বালের ছবি,,,",0,entertainment
"অনেক বার দেখা হয়ে গেছে, ভালো একটা ছবি হয়েছে মনপুরা।",0,entertainment
"ভাই যদি দয়া হয় তাহলে আমিন খানের, এ্যাটাক, ছবিটি দিন ভাই",0,entertainment
নাটকটি দেখে বেশ ভালো লাগে,0,entertainment
"এগুলোর একটা সুষ্ঠ সমাধান রয়েছে।<br />কিছু বাচ্চাদের এনে যদি পবিত্র কুরআনের হাফেজ বানানো হয়,তাহলে আস্তে আস্তে সেই হাফেজ গুলি আরো পতিতার বাচ্চাদের এনে কোরআনের আলোয় আলোকিত করে, আস্তে আস্তে তারা তাদের মা বোনদের ঐ পথ থেকে আলোর পথে আনবে।",0,entertainment
কার কাছে এই মেয়েকে ময়ূরির মতো লাগে।,0,entertainment
এনা দের কে মানহানীর দায়ে পুলিশের আওতায় এনে কঠিন শাস্তির বিধান করা উচিত !,0,entertainment
খুবি কষ্টদায়ক র্শটফিল্মটি.. শেষে কান্না চলে আসল,0,entertainment
ফালতু ব্যবহার,0,entertainment
এরকম নায়ক কী শাবনূর এর সাথে মানানসই,0,entertainment
বাংলাদেশে কি সুদর্শন ছেলের অভাব ?? নায়কের একটা ডায়লগ শুনলাম না এই ট্রেইলার নাকি অনেকের ভালো লেগেছে 😀হায়রে বাঙ্গালি,0,entertainment
সত্যি অসাধারন মুভি,0,entertainment
বাংলা ভারত শাকিবের,0,entertainment
গানের সাউন্ড নাই কেন সালা,0,entertainment
ভাইরে ভাই এইটা এইটাই দেখার বাকি ছিলো।আমারে কেউ মাইরালা😩😩,0,entertainment
আরফান নিশু ভাইয়ার ভক্তরা আমার কমেন্টে লাইক দিয়ে হাজিরা দিয়ে যাও!,0,entertainment
"আমার প্রথম ভালোবাসা,,,,,,<br />যদিও ছোট ছিলাম,,,,,,,",0,entertainment
রিয়াজের ছবি বলে কথা অনেক ভালো লাগলো,0,entertainment
বঙ্গ বিডির সেরা কাজ ছিলো এটা,0,entertainment
ভাবির নামটা কি বলা যাবে,0,entertainment
এই বিল্ডিং এর পাশে একটি মাদ্রাসা ও একটি মসজিদ আছে এখানে থেকে নষ্ট মেয়ে দিয়ে এসব করা কি ঠিকতাও আবার ভিলেন চরিত্রে ঐ মাদ্রাসা মসজিদের প্রতিষ্ঠার বড় ছেলে মাছুম,0,entertainment
আয়লাভ শাকিল খান ভাই,0,entertainment
"আমি একজন ভারতীয় হয়ে বাংলাদেশের গ্রামের ভালো নাটক ও ছবি খুজে বেরাই। মনপুরা,সমুদ্রবিলাস,মহারাণী,কুটুম্বপুর জংসন এর পর‍ অজ্ঞাতনামা সপরিবারে দেখেনিজে ধন্য হয়ে গেলাম।এইরকম দুর্দান্তকাহিনী,লোকেশন,ভাষ্যর সমন্বয়েছবি আরো আরো চাই।",0,entertainment
ব্রাম্মনবাড়ীয়ার মানুষ কথায় বুঝা যায়,0,entertainment
অনেক সুন্দর হয়েছে ধন্যবাদ,0,entertainment
অনেক ভাল লাগল অনেক সুন্দর গান টা আমার ভালো লাগে সোপারনায়কবাবপি,0,entertainment
"হায়রে বাংলাদেশের মুভি,,এই ধরনের মুভি আর হবে কি বুঝতে পারিনা,, আমি জসিম ভাইয়ের মুভি খুবই পছন্দ করি,, তার মুভির তোলনা হয়না। আমি সৌদি থাকি। 00966533485366 lmo",0,entertainment
বাংলা মুভি এত সুন্দর হয় তা এখন কেবল ইতিহাস😥😢,0,entertainment
"নায়িকা টা খুব সুন্দর, আই লাভ ইউ নায়িকা",0,entertainment
"দারুণ নাটক,,,,",0,entertainment
এই ছবি টি ছোট বেলায় চট্টগ্রামের টাইগার পাস নেভি হলে একবার দেখে ছিলাম,0,entertainment
সত্যি এই দুইজন অভিনেতা মোশাররফ ভাই ফারুক ভাই অসাধারণ,0,entertainment
নাটকটিতে ২:২৫ সেকেন্ডের মাথায় একটা বড় ভুল আছে।,0,entertainment
লুইচ্চা,0,entertainment
বাংলাদেশ,0,entertainment
নিসা ফালটু,0,entertainment
সাবিলার জন্য নাটক টিতে লাইক দিলাম,0,entertainment
"আমার মতো শেষ সারির ইউটিউবারদের একটু দয়া করুন ভাই, বোন, দাদা ও দিদিরা। ভিডিও গুলো আপনাদের ভালো লাগবে, কথা দিচ্ছি। এই গরীব ছেলের চ্যানেলটি বেড়ে উঠতে এবং স্বপ্ন পূরণে সাহায্য করুন প্লিজ, এটাই আমার ইউটিউব চ্যানেল।",0,entertainment
এতো সুন্দর ভাষা ব্যবহার এখনকার বাংলা মুভি তে দেখা যায় না.মুভিতে এমন ভাষা ব্যবহার করা উচিত,0,entertainment
কি করে তোকে বলবো তুই কে আমার আয়না পথে চলো আজ পানামা,0,entertainment
নদির সব ফাটাফাটি,0,entertainment
এখন গান টা নিয়ে ও জিৎ দার সমন্ধে বাজে কথা কেউ বলবেনা আশা করি। জিৎ দা মোটেও মুসলীম বিদ্বেষী নন । হলে বাদশা দা ডনে ঈদ মোবোরোকের মতো সুন্দর গান দিতেন না ।,0,entertainment
ভাই ছবি টার লিংক হবে,0,entertainment
পালতু পরিচালকের পালতু ছবি,0,entertainment
নাইস মুভি,0,entertainment
"আমিও প্রায় ৭ টা স্কুল পরিবর্তন করেছি,কত সৃতি কত বন্ধু ফেলে আসতে হয়েছে 😞😞<br />অনেক মিসকরি ওই সব সৃতি আর বন্ধু গুলো কে জানি আর পাবোনা ওই সৃতি আর বন্ধু গুলোকে।তার পরেও ওই সৃতি গুলো জমা থাকবে মনের একটা কোনে,ভুড়ো হয়ে যখন মৃত্যুর অপেক্ষায় থাকব এই সৃতি তখন মনে মনে ভাববোআর হাসবো আর চোখের কোনে পানি এসে ভিজে যাবে নিজের গাল😞😞",0,entertainment
গরুর মাঠে মার খাবা আবার,0,entertainment
সুকরিয়া ভাই,0,entertainment
জসিমের আরো ছবি চাই,0,entertainment
নায়কটার নাম এ আর মন্টু। তার বাসার পাশেই আমি ছিলাম। তাকে খুব ভাল করেই চিনি...,0,entertainment
শহিদ,0,entertainment
একদম বাজে হইছে,0,entertainment
আমি যদি সে প্রতিযোগিদের যাইগাই থাকতাম সেই বিচারক কে জুতার বাড়ি দিয়ে আমিই হয়ে জেতাম আসল হিরু,0,entertainment
এই নাটকের জন্য ধন্যবাদ,0,entertainment
বাংলা চলচ্চিত্র আবারও প্রাণ ফিরে পাবে এই রকম অভিনেত্রী যদি তৈরী করা যায়জয় হোক বাংলা চলচ্চিত্র র জয় হোক শাবনূরের,0,entertainment
সেই মজা পাইছি আর কোন আবাল গুলা ডিসলাইক দিছে আর হ্যা আজকেই একটু আগে মাত্র চ্যানেল এ 🐍🐍🐍এর খেলা দেইখা আসলাম তালাশ ফিড ব্যাক 🐸🐸🐸,0,entertainment
দাডিওয়ালার নাম তাও জানি না হালারে আগে কখনো দেখি নাই,0,entertainment
আগের দিনের পুরানো ছবি গুলো বেশি ভালো ছিলো আর এখনকার ছবি না কি ঘোড়ার ডিম বানায়?,0,entertainment
পুরাই ফালতু নাটক....,0,entertainment
বাপের টাকা মুভি টা আপলোড করবেন প্লিজ,0,entertainment
চোট ছেলে দের দিয়ে সেক্স করাতে পারবে,0,entertainment
আর ঐ বান্দরের মতো চুল ওর নাম কি রে লটির বাচ্চা,0,entertainment
অসাধারণ গল্প--------অনেক ভাল লাগলো,0,entertainment
"মান্নার ছবিতে অনেক ভাল কাহিনি থাকে ছবিটা খুব ভাল লাগল, চোখে জল এসে গেল।মান্না তুমি ভাল থেক ওপারে। সালাম বস।",0,entertainment
তোমার ছিলাম তোমারী থাকবো,0,entertainment
তার এর নাম কি,0,entertainment
এত কথার নাটক কেউ দেখেনা,0,entertainment
নায়ক আসলে কে?,0,entertainment
সানাই য়ের মত এই সব নষ্ট নারীর কারণে আজ আমাদের নারী সমাজের এই অবস্তা শালী দরে কুত্তা দিয়ে কিছু করানোর দরকার না হয় এই সব দেখে মহিলাদের মানসম্মান কমবে,0,entertainment
অসাদারন ত্রকটা নাটক বাস্তব কাহিনি নিয়ে নাটকটা করার জন্য বস নিশো ভাই ত্রবং পরীচালক ভাইদের অনেক ধন্যবাদ,0,entertainment
নাটক হলেও বাস্তবে অনেকের জীবনে এমন টা ঘটে যায় ।মেয়ে মানুষের মন এমন ই হয় কখনো পাথর আবার কখনো আইস এর চেয়ে ও নরম ।,0,entertainment
নিঃস্বার্থ ছবির লিগ টা কেউ দিতে পারবেন,0,entertainment
ধারাবাহিক পর্ব নাটক দেখার আগ্রহ কেটে যায় যখন আপনারা দেরি করে আপলোড করেন...তাই আপনাদের কাছে একটা একদিন পর পর যেন আপলোড করেন ✌,0,entertainment
বাউতামি শুরু কইরা দিছত দেখা যায়।এই নাটকের নাম হইলো সেল্ফি,0,entertainment
"আমার খারাপ লাগে এ কনকার বাংলা মুভি দেকলে,,,,,,গাজা খাইয়া মুভি বানাই director রা,,,,,,,,,,,১৯৯৫ সালের জেই কাহিনী বতমানে ও তাই,,,,,পাথক্য এসেছে কাপড় পরিধানে।।।",0,entertainment
ফুটবল,0,entertainment
এবার বাংলাদেশ ও মনে হয় এই ফালতু এর সাথে নেই,0,entertainment
ছবিটা দেখার মতন ছবি কোব সুন্দর,0,entertainment
সেই কবে ছোট বেলায় বিটিভি তে দেখেছি আজ আবার অনেক পর দেখলাম,0,entertainment
ভাই আপনি এখন যে ক্যামেরা ব্যবহার করছেন তার মডেলটা কি,0,entertainment
আমার ভালবাসা,0,entertainment
"নাটকা আমার জীবন সাথে মিলে গেছে,,,আমি আমার gf কে মেরে জেলে যাবো",0,entertainment
পাঁচ ওয়াক্ত নামাজ আদায় কর। যত বাদা আশবে সব আল্লাহ তায়ালা বিদায় করে দেবে🌎,0,entertainment
"কিছুকিছু মানুষ আছে খারাপ কমেন্টদেয় কিন্তু ভুজলামনা, থাকে বাংলাদেশে গান গায় ইনডিয়া",0,entertainment
সাকিব খাঁনের ফ্যান কারা,0,entertainment
অসাধারণ ছিল নাটক টি।,0,entertainment
কাজী পরিবার সিনেমার নক্ষত্র। সমসাময়িক বিষয়াবলী সেলুলয়েডের পর্দায় এমনভাবে উপস্থাপন করার সৎ সাহস অন্য কোনো পরিচালক দেখাতে পারেনি। সালাম জানাই কাজী হায়াৎ ও কাজী মারুফকে।<br /><br />শিক্ষণীয় ও সমাজ অসচেতনতামূলক এমন সিনেমায় শেখার আছে অনেককিছু।<br /><br />কবির<br />গবেষক চট্টগ্রাম বিশ্ববিদ্যালয়,0,entertainment
মাঝে মাঝে রাজনীতিবিদ দের নাটক সিনেমাকেও হার মানায় 👿,0,entertainment
জান আমার জান ছবি দিন প্লিজ,0,entertainment
এই খানকির পোলারা চলোচিতরো দংসোকরে কি নায়াক,0,entertainment
অপর্নার মেকয়াপটা খুব খারাপ দেখাচ্ছে৷ ছেলেদের মত লাগতেছে তারে,0,entertainment
"ভালো লাগল শর্টফিল্মটি,, শেষ দৃশ্যে খুব কষ্ট দায়ক",0,entertainment
মোয়েটার ফেমিলি বলতে কি কিছু নাই।। অবাক আমি,0,entertainment
মিডিয়ায় ভালো কিছু তুলে ধরুন এ সমস্ত বেহায়া মেয়েদের মিডিয়ায় তুলে ধরবেন না,0,entertainment
আমার প্রিয় বন্ধু শাকিব খান ও অপু বিশ্বাস,0,entertainment
জামিল মানেই তো নতুন কিছু,0,entertainment
ধন্যবাদ এই মুভিটা আপলোড দেওয়া জন্য,0,entertainment
বালের গান।,0,entertainment
"ছবিটির কাহিনী,,,, ,,সুন্দর,,,, রুবেল আলেকজান্ডার অসাধরন,,,,",0,entertainment
স্কুলে যেতে চায় যাক তাতে এতো মারামারি কান্নাকাটি করার কি আছে য?,0,entertainment
দীপু নাম্বার ২ গল্প টি পড়ার পর মুভি টি দেখতে এলাম।<br />এই মুভি গুলোই বাংলাদেশের অহংকার। <br />ধন্যবাদ জাফর ইকবাল স্যার কে এত সুন্দর গল্প লেখার জন্য।,0,entertainment
এরাসতা চেরেদিয়ে জদি ভাল হতে চাও তাহলে দেকবে আল্লাহর রহমতে তুমরা সুনদর ভাবে জীবন কাটাতে পারবে সবাই তু তুমাদের কে চিনেনা তুমরা গারমেনসে কাজকর দেকবে সবটিক হয়ে গেচে অতবাকুনকিচুর জদি সাহাজ লাগে তাহলে জুগাজুগ রকতে পার আমার নাবারে 01918686917,0,entertainment
আপনাদের উদ্দেশ্য বলছি কাটা কাটি করে মুভি ডাউনলোড দিবেন না প্লিজ।,0,entertainment
জয় ভাই আপনার প্রোগ্রাম নাম্বার ওয়ান।।আমি সৌদি আরব থেকে দেখি আপনার শো কম হলেও চাই ।।আমার জন্মভূমি বাংলাদেশের। জয় ভাই আপনাকে ধন্যবাদ,0,entertainment
"গল্প ভাবনা খুবই ভাললাগলো, চোখে পানি এসে গেল,",0,entertainment
খুবসুন্দর একটা সচেতন মূলক নাটক দেবার জন্য মেহেজাবিন এবং আরফান ভাইকে ধন্যবাদ।,0,entertainment
খুব ভাল ছবি কাতার প্রবাসী ----০০৯৭৪৩০৪৫৮৪১৬,0,entertainment
ভালোবাসা কখনও জোর করে হয় না। ভালোবাসা হয়ে যায়। nisho vai love you,0,entertainment
"দয়া করে জসিমের ছবিগুলো আপলোড দিবেন,,বীর বাহাদুর,,,, হাবিলদার,,, ডাকাত,,,উচিত শিক্ষা,,, হাতকরা ফাইভ রাইফেল,,,, আরো যা আছে জসিমের ছবিগুলো আপলোড দিবেন।",0,entertainment
জুতা জুরা দে,0,entertainment
ভালো লাগে সাব্বির আর অহনা আমি ইংল্যান্ড থেকে,0,entertainment
সেই ছোটবেলা মোবাইল ছিলো না কত কষ্ট করে অন্যের মোবাইল থেকে ছবিটা দেখছিলাম আবার ছবিটা ১৬-০৯-২০১৯ সালে দেখলাম। সেই দিনগুলো চলেই গেলো আর ফিরে আসবে না ।,0,entertainment
মানসিক রুগী,0,entertainment
বিয়া হই নাই তাই দুধ এত বড়। আর বিয়া হইলে যে কত বড় হইত।কে কে দুধে হাত দিয়েছে। সানাই,0,entertainment
সত্যিই খুব সুন্দর সিনেমা একেবারে দেখার মতো,0,entertainment
ফালতু। যে একবার চলে যায়। তাকে মেনে নেয়া পরের বার বোকামি,0,entertainment
আমার ফাষট মভি ছবি এ বাদন জাবে ছিরে,0,entertainment
হ্যালো বন্ধুরা আমাকে তোমাদের বন্ধু বানিয়ে নাও আমি তোমাদের জন্য ভালো ভালো ভিডিও বানাবো,0,entertainment
আর কতবার বলবো <br />আজকের ক‍্যাডার<br />আজকের দাপট আর<br />ঠেকাও মাস্তান<br />এই তিনটা ছবি দিন please please please<br />ভাইয়া,0,entertainment
ফারিয়ার বিষয়টা খুবই বিরক্তিকর লেগেছে 😡,0,entertainment
কিং অফ বাংলা ফরিদ এন্ড রাজিব,0,entertainment
আর নায়ক খোজে পাইলো না 😂,0,entertainment
শেষের সিন টুকু অনেক কষ্টের!!!!😥😥,0,entertainment
এটা কোন নাটক হল????? ফিনিশিং নাই...!!,0,entertainment
আশা করি ভাল হবে,0,entertainment
"যার হারিয়ে যায়, সে বুঝে আপনজন হারানোর বেদনা কত কষ্টের। এতো সুন্দর একটা ছবি উপহার দেওয়ার জন্য পরিচালককে ধন্যবাদ।",0,entertainment
তেজ ফার্মের মুরগী,0,entertainment
অল্প অল্প করে জীবনের গল্প &quot;&quot;&quot;&quot;&quot;এই গানটার জন্যই মুভিটা অনেক বার দেখেছি।।ভাল লাগার মত একটা মুভি।।,0,entertainment
নিরানন্দের মধ্যে আনন্দের অনুভূতি,0,entertainment
কেউ কি বলতে পারবেন এই ছবিটি কলকাতার টার নাম কি???,0,entertainment
ভালবাসার চেয়ে কোন অস্ত্র আজও তৈরী হয়নি ৷আর কোন হবে না তৈরী &quot;৷ভালবাসা দিয়ে পৃথীবিকে জয় করে নিতে হয় ৷বলদ মজিদ তাই করেছে ৷তাই বলি ভালবাসতে শিখুন ৷,0,entertainment
বেটা তোর লজ্জা সরম নেই,0,entertainment
"এই ছবি টা আমি ১২ বার দেখেছি,,,",0,entertainment
ইমন যে নায়ক বানাইছে ঐ শালা পাগল,0,entertainment
ভিডিও এটা আবারও এটা না ডিলিট করসে,0,entertainment
তোর কোন কাজ নেই।আজ য়দি তোর বোন হতো আর তোর বোন যে করেনাতার কী প্রমাণ আছে।,0,entertainment
নাটকের পরিচালকে অনেক অনেক ধন্যবাদ জানাইশিক্ষা মূলক নাটকটা পরিচালনা করার জন্য,0,entertainment
ছবি টা দেখতে চাই,0,entertainment
অশ্লীলতার হাতছানি সোদাইতাছো তোমরা বালের নাটক দিয়া 🌚🌚,0,entertainment
আসলে অনেক ভাল লেগেছে<br />এক কথায় অসাধারণ♠♠♠♠♠,0,entertainment
ফালতু!<br />পরবর্তী নাটক গুলি দেখে করবেন।,0,entertainment
বাংলাদেশে আইন বলে কিছু নাই ।যার ক্ষমতা বেশি সে যা চাইবে ইচ্ছা করবে তাই আইন,0,entertainment
নাটক তো না যতো সব কিত্তি।,0,entertainment
"ইসস,দুনিয়াতে যদি সত্যিই এমন মানুষ থাকতো,তাহলে অই সুন্দর মনের অসহায় নারীগুলার কষ্ট কিছুটা হলেও দূর হত...",0,entertainment
উপস্থাপক মেয়েটা ভাল ছিল। কিন্তু তার পোশাক টা পুড়াই ফকিন্নি মার্কা।,0,entertainment
"এত দিনের চেনা তুমি তারপরও অচেনা,,,, <br />Demon 😶😶",0,entertainment
কে আপনি ভলে ভালো হতো ।,0,entertainment
টাইটেলটা এইরকম হতে পারতো কে হবে রোস্ট রানা 😃,0,entertainment
এটা সাজানো🙃👎,0,entertainment
অপেক্ষায় রইলাম গানটার 😊😊,0,entertainment
"সেই ছোটবেলাই দেখেছিলাম শুধুমাত্র মারামারি এবং অন্যান্ন কিছু মনে আছে,,,<br />আজ আনুমানিক ২০/২২বছর পর দেখছি,,,",0,entertainment
এরা বিচারক হয় কিভাবে,0,entertainment
তো নোংরামিকে আমারা 👏👏👏👏,0,entertainment
ফালতু ছবি... হায়রে... এই হলো বাংলাদেশের চলচিএ। ছিঃ ছিঃ ছিঃ...,0,entertainment
দুধ টিপে দাও!!😹,0,entertainment
তুমি কোথায় যাচ্ছ খালা,0,entertainment
এক কথায় অসাধারণ৷<br />সমাজের এই বাস্তবচিত্রগুলো তুলে ধরার জন্য ধন্যবাদ৷,0,entertainment
আমার জীবনের এক কাহিনী এই ভিডিও টা দেখে আমার মনটা ভরে গেল ভাই কিন্তু আমি নেসা করিনাই ভাই কিন্তু এই ভিডিও টার সাতে আমার জীবনেরমিল আছে ভাই কিছু লোক আছে ভালো সংছার খারাপ লোকজন ভালো থাকতে দিবেনা 100%100%,0,entertainment
সুনাই পাগল হয়ে গেছে পাগলা গারদে পাঠান।,0,entertainment
আমার প্রেমের কাহিনী,0,entertainment
খুব সুন্দর মুভি। শাবনূরের অভিনয় অসাধারন,0,entertainment
কাহিনী ও চিত্রনাট্য খুবই হাস্যকর,0,entertainment
"নিশো ভাই + মেহজাবীনআপাএদের নাটক+ অভিনয়অতুলনীয়,সতো চিন্তার মধ্যে ওভালো লাগল",0,entertainment
জানতাম বাল চুল পাকলে বিচারক হওয়া যায় কিন্তু এখন দেখি জিনিসটা আসলে তা নয় । কাঁচা বালেও বিচারক হওয়া যায় । সালের সেরা কৌতুক হয়েছে এই কয়টা ছাগলরে বিচারকের আসনে বসিয়ে ।,0,entertainment
ওদের জুতা দিয়া পিটানো উচিত ওরা নিজেদের কে অনেক বড় মাপের মানুষ ভাবছে কিন্তুু ওরা জানেনা ওরাযে মানুষই না নিজে জাকে বড় বলে বড় সেনয় লোকে যাকে বড় বলে বড় সেই হয়।,0,entertainment
আসলে ওই একটা পাগল জামাই,0,entertainment
"ছানি লিওন ফেল নিপুনের কাছে,",0,entertainment
ছোটকাল থেকে যতবার দেখে আসছি প্রতিবার চোখের জ্বল ঝড়ে 😥,0,entertainment
আরেকটা কথা শুন তরার ভিডিও টা দেখে আমার যেইMB টা নষ্ট হয়েছে এটা ফেরত দে নইলে তদের চ্যানেল আন সাবস্ক্রাইব করব,0,entertainment
এ সব নাটক মেয়েদের সাহস বারে বেপরদা হচ্ছে,0,entertainment
"আমার দেখায় সব থেকে ভালো ছবি ছবি টা দেখে কান্না থামাতে পারেনি<br />অসাধারণ একটি ছবি একদম নিখুঁত অভিনয় ,মান্না ভাই আমাদের টাঙ্গাইলের অহংকার আমাদের টাঙ্গাইলের গৌরব,মিস ইউ মান্না ভাই উপরেও ভালো থেকো দোয়া করি আল্লাহ যেন তোমাকে জান্নাত দান করেন,,,,আমিন",0,entertainment
ভাই তুই পুরা ইত্যাদি,0,entertainment
"এতো সুন্দর গল্প আপনারা কোথা থেকে পান,,,",0,entertainment
নতুন ভিডিও এর অপেক্ষায় ✌,0,entertainment
মিথিলার মা বাবার জন্য অনেক কসট্য হয়,0,entertainment
"ছবিটি বাস্তবতার সাথে পুরোপুরি মিল আছে, একটা নারীর কারনেই সংসার নষ্ট হয়ে যায়, <br />আবার সেই নারীরাই পারে একটা সংসার গড়ে তুলতে,,",0,entertainment
আমি এদের কে ঘৃণা করি না আমি ঘৃণা করি ওই সব পুরুষদের যারা এই মেয়েদের পতিতা হতে বাধ্য করে। যারা এদেরকে পতিতা বানায়। ছি ছি এসব পুরুষদের উপর।,0,entertainment
মাকে যারা ভালোবাসেন তারা হাত তুলুন☺💕 i love u mom but i really miss u😞😌💔,0,entertainment
খুবই সুন্দর নাটক<br />মোশারফ করিম খুব সুন্দর অভিনয় করে,0,entertainment
এখনো দেখা হয়নি আমার কিন্তু মানুষের কমেন্ড দেইকা মনে হইতাছে তামিল নাটককের চাইতেও মজা হবে,0,entertainment
ফুল ছবি দেখান,0,entertainment
জার নিজের ছুল ঠিক নাই সে আবার ওন্নের দোশ দরে পালতু লোক,0,entertainment
আফা কঠিন চাপ দিছিল,0,entertainment
দেখে বোঝা যাচ্ছেনা যে,0,entertainment
বাস্তবে জদি করে এরা মানুষ নয়<br />জানোয়ার,0,entertainment
এই মুভিতে দুইটি মেসেজ দেওয়া আছে(1) প্রেমের সম্পর্কে পরে অনেকেই অবৈধ মেলামেশা করে এবং অতি উত্সাহের কারনে তা ভিডিও করে এবং বিপদে পরে।(2) MLM ব্যবসা একটা প্রতারণামূলক ব্যবসা এতে জরিত হয়ে অনেকেই নিঃস্ব হয়েছে যেমন (ডেস্টিনি),0,entertainment
কপাল খারাপ হলে এমন হয়,0,entertainment
"আশা করি ভিডিও অনেক ভালো হবে,,",0,entertainment
ছবিটা অসাধারন।<br />অনেক দিন পর আবার দেখলাম।<br />খুব ভালো লাগলো।,0,entertainment
আমিন খানে মুভিজ খুব ভাল লাগে,0,entertainment
সাদা মনের শিলপী সাদা মনের গান টা সুনে খুব ভালো লাগলো।,0,entertainment
ছবিটি অনেক ভাল।রাজু আহসান। পাকুল্লা টাংগাইলসদর,0,entertainment
দারুন লাগলো ছবিটি,0,entertainment
গানের প্রতিটি কথার লজিক আছে!,0,entertainment
"রিয়াজ সাকিল খান, বিয়ের ফুল, ছবি টা আপডেট দিন",0,entertainment
আমি লমু দায়িত্ব,0,entertainment
"আগে যখন শুক্রবার আসতো তখননিয়ে দেখতাম! যখন ৩.২৫ সময় ,...এখনো ছবিগুলো দেখি আর সেই কথাগুলো মনে পরে",0,entertainment
রুবেল কোন নায়ক হইল,0,entertainment
দারুণ এরকম ক্লাসিক সিনেমা পারে আসল ঘটনা বলতে,0,entertainment
তুমি শুধু আমার,0,entertainment
কত সালের সিনেমা এটা?,0,entertainment
"সালমান শাহ্ তুমি এখনো বেঁচে আছো শত কোটির দর্শকের হৃদয় জুড়ে, ভালোবাসি তোমাকে",0,entertainment
আপনারা জান্নাতের বাকি পর্ব গুলা দিচ্ছেন না কেনো?,0,entertainment
"ছবিটা হলে ফ্লপ ক্ষেয়েছে,,,দেখা যাক ইউটিউবে কি হয়,",0,entertainment
"কি বলব অসাধারণ,, সত্যি দেখার <br />মত,অনেক ভাল লাগে,,তাই মাঝে মাঝেই<br />দেখি,,,",0,entertainment
পপি ছবি চাই,0,entertainment
আসুন আমারা সবাই নামাজ পড়ি,0,entertainment
পরোকিলের জন্র আগুনে জলতে হবে সতি ঘটনা ত্রই সব কাজের কারনে,0,entertainment
"খুব ভালো হয়েছে, সিনেমা হিট হবে মনে হয়।",0,entertainment
"মাশাল্লাহ দেখছি নতুন করে, ভালো লাগছে খুব",0,entertainment
হায়রে বাংলা সিনেমা।🤣<br />অবতার R Avatar এর মাঝে কোন কালেকশন নাই।🤣🤣🤣<br />বাংলা সিনেমায় শুধু পাছা র ব্রা দেখিয়ে আউল ফাউল নাচই পারবা কোনো একটা কাহিনি নিজ থেকে জীবনে বানাইতা পারবা না।,0,entertainment
অসম্ভব খারাফ হয়েছে সমাপ্তিটা,0,entertainment
নিলা আপু আপনার নাটক গুল আমার কাছে অনেক ভালো লাগে আর আপনাকে অসাধারন লাকছে💖💖,0,entertainment
ছবি টা মূলত কমেন্ট গুলো পড়েই দেখা,0,entertainment
এইটা কবে আপলোড হবে অপেক্ষায় রইলাম 😘😘,0,entertainment
বয়ফ্রেন্ড ফিরে এসে কি দুদু খাবে নাকি😜😜,0,entertainment
ছোট বেলায় বিটিভিতে ছবিটা দেখতাম কিন্ত এত এট দিতযে কখনই ফুল মুভিটা দেখতে পারতাম না।,0,entertainment
আপনার প্রিয় অভিনেতা কে<br />1 মোশাররফ করিম<br />2 আ খ ম হাসান,0,entertainment
ছবিক কাহিনি ভাল ছিল কিন্তু কাটা কাটি করে দেওয়া কোন মজাই নেই দেখে।,0,entertainment
আপনাদের ভালোবাসা আমাদের অনুপ্রেরণা।♥,0,entertainment
বিচার হবেই ইনশাআল্লাহ,0,entertainment
চান্দি ছিলা বান্দিরপুত ৷<br />সেই কথা,0,entertainment
পিউ পিউ করে কেন পিউ পিউ এটা করার কারন কি,0,entertainment
তুলনা হয় না অসাধারণ,0,entertainment
এখন নিয়মিত টাপাবে পরে বিয়ে করবে 😃😃,0,entertainment
পন্ডিট মশাই আপনার বোনের জামাই মানে দুষ্ট জামাই,0,entertainment
শাকিব খান বস তুমি একটা জিনিস তুমি যে নায়িকার সাথে সিনেমা করো সেই নায়িকা সুপারহিট হয়ে যায়,0,entertainment
এইগুলো কে বিচারকের আসনে বসিয়ে ছে কেনো,0,entertainment
স্বপ্ন দেখা ভালো।স্বপ্ন দেখানো ভালো না। যদি পুরন করতে না পারে,0,entertainment
ইরো আলমের নায়ক করলে এর চেয়ে আরো ভাল হত।,0,entertainment
"ইসলামে গান হারাম নাহ ,তবে যদি গানের ভিতরশিরক থাকে অথবা যদি বাদ্যযন্ত্র ব্যবহার করা হয় ,তবে সেটা সম্পুন হারাম!",0,entertainment
করিম ভাই ফ্যান্টাস্টিন,0,entertainment
টিনের চালে কাউয়া তুমি আমার সাউয়া। সালার পো নিজের চুল দাড়িই তো ভালো করে কাটে না। আবার বিচারক সোদায়। 🖕🖕,0,entertainment
"সত্যজিৎ রায়ের প্রতিফলন ঘটেছে<br />অসাধারন চিত্রনাট্য, <br />সম্পাদনা, সর্বোপরি অভিনয় ও পরিচালনা<br />সর্বোশেষ আপি করিম<br />ওনার ফিটনেসে মুগ্ধ হলাম<br />চরিত্র টা কে justified করেছে",0,entertainment
ভালোবাসা এতো কষ্ট কেন,0,entertainment
ওরে বাবা রে। ওরে মা রে,0,entertainment
এমপি হলে ধুদের দাম কমবে,0,entertainment
অসাধারন গান।,0,entertainment
লোভে পাপ পাপে মৃত্যু,0,entertainment
নারীর কারনে,0,entertainment
"অনেক ধৈর্য ধরলাম, আর সম্ভব হচ্ছে না।",0,entertainment
দৃষ্টিকটুর কস কা দৃষ্টিকটু। না পারস বাংলা আমি শিওর ইংরেজিও পারস না। আমেরিকায় বইসা বাপের ট্যাকা নষ্ট না কইরা বাংলাদেশে ফেরত আও আর কাম কাজ করো। মা বাপ কিছুতো ফেরত পাইবো। নাইলেতো টোটাল লস।,0,entertainment
তার মুখে ছু ছু করতে ইচ্ছে করছে আমার,0,entertainment
উর্দু ডাবিং করা একটা ড্রামা দেখে তুর্কিশ ড্রামার ফ্যান হয়ে গেছি😍😍 তাই এটাও দেখতে আসছি,0,entertainment
এইটাকি নায়ক হইল,0,entertainment
"এতো দেখি তাও মন ভরেনা, মন চাই<br />যেন সারাদিন দেখি,,, এত ভালো লাগে এই নাটক টা আমার।মাঝে মাঝে আমার কেন জানি কান্না পাই কেনন তা জানিনা,টিউন টা তো অসাধারন,,I love very very much this natok and tune...",0,entertainment
দৌলদিয়া মাগি পারা. হোম সারভিস দেয়া হয়. যোগাযক করুন . আমি আরমান ভাই 01992077773,0,entertainment
জীবনের সেরা ছবি,0,entertainment
তর দুদ এত বর তর হেডা যে কত বর কে জানে,0,entertainment
দেখা ছবি গুলো কেন দিতেছেন যদি পারেন তাহলে নতুন কিছু আন কমান ছবি দিন ভাই যদি নতুন কিছু পাই তাহলে আপনার চেলেনের ছবি দেখবো তার আগে আর দেখবো না,0,entertainment
এই বালের নায়িকা টারে আমসর কাছে পয়সার ও ভাল লাগে না মুখের ফাক কত বর। আমার কাছে খালি তৃষা আর মেহজাবিন চৌধুরী আর ওপার বাংলার সবচেয়ে ভদ্র নায়িকা যার কোন হিউমার নায় কোয়েল মল্লিক রে ভাল লাগে,0,entertainment
সপরিবারে দেখার মত একটা মুভি..... জসিম ভাইকে স্মরণ করছি খুব।,0,entertainment
আমার চোঁখের পানি দরে রাকতে পারি নি স্যতি মহরম জসিম ভাই জেতো গুলোচবি করচে দেখার মতো এবং বুজার মতো,0,entertainment
অনেক সুন্দর একটা ছবি। শেষের দিকে চোখে পানি এসে পড়েছে,0,entertainment
দেখা শেষ!😍😍<br />মোস্ট ফেভারিট ড্রামা❤❤❤,0,entertainment
শাহিন আলম যে নাম্বার নয় টা দিল সাহেরাকে আর দুটো কোথায়।,0,entertainment
"এই এপিসোড এক মাস আগেই দেখে নিছি। আজ আপলোড না দিয়ে পরের এপিসোড নিয়ে কাজ করলে সবার জন্য ভালো হয়। প্রতিদিন এই চ্যানেলে ডোঁ মারি, কবে পরের এপিসোড আপলোড হচ্ছে। প্রতিবারই আশাহত হই। আশা করবো পরের এপিসোড নিয়ে চিন্তা করবেন।",0,entertainment
"আমি আর জুয়া খেলব না, না না না",0,entertainment
বাংলার মহানায়ক কিং খান মহানায়ক মান্না,0,entertainment
পারবে বলে করেছে,0,entertainment
ছোট বেলাটা কেটেছে এই মুভি গুলো দিয়ে।মৌসুমি এবং ফেরদৌস কে খুবই ভালো লাগে😘😍,0,entertainment
ছবিটা পুরোটাই দিতেন,0,entertainment
আল্লাহ তুমি সকল প্রবাসী ভাই বোনদের হেফাজতে রেখ,0,entertainment
এক কথায় অসাধারণ নাটক,0,entertainment
কিছু কলার নাই।।,0,entertainment
অপূর্ব তো অপূর্ব,0,entertainment
যাষ্ট আপনার জন্যই বসে ছিলাম,0,entertainment
"আমিন খান থাকতে৷৷৷ <br />এসব ফালতু ছেলে দিয়ে মুভি করানোটা মুরখতা,,,,,,,,, সালা বালের পরিচালক,,",0,entertainment
"মুভি টা যত বার দেখি তত বার সেই সোনালি দিন গুলোর কথা মনে পড়ে, নেভি ব্লু প্যান্ট, আর সাদা শার্টের সেই হাজার স্রিতির দিন গুলো!আহা",0,entertainment
তুমি কি মরবে না একদিন তুমার এই হাল হবে।তুমার মুখে লোকে তু তু ফেলবে।,0,entertainment
ফাজলামির একটা সীমা থাকা দরকার। এইটা সাইক্লোনমুভি না৷,0,entertainment
অনেক সুন্দর একটি ছবি কিন্তু শেষে নায়ক নাইকার আত্নহত্যা ঠিক হয় নাই।এখন বর্তমানে ছেলে মেয়েরা আত্নহত্যা করার সাহজ পায় বেশি।আত্নহত্যা কোনো কিছুর সমাধান হতে পারে না।,0,entertainment
আপনারা যারা নাটক বানান তাদের কে বলছি এগোলো ছেরে আলু পটল বিক্রি করো তোমরা নাটকের মিল দাওনা যদি নাটক করো তাহলে নাটকের মিল দিও,0,entertainment
কবিরাজ সজীব সম্রাট <br />০১৭১৮৪৬১৫৪৯,0,entertainment
ভাইয়া এই ফিল্মের যত গান আছে সব গুলো ফুল এসডি ভাবে আপলোড দিবেন প্লিজ ভাইয়া,0,entertainment
এই মুবিটি দেখে একটু আবেগ ময় হয় গেলামআর ও একটি মুবি বাবা কেন চাকরদেখলে শুধু কান্না আশে,0,entertainment
বিচারকদের ভাবটা লিমিটের বাইরে ছিলো,0,entertainment
এই মুভির 2 পাট করলে আরো অনেক ভালো হবে।,0,entertainment
"আমার একটা হট বয়ফ্রেন্ড দরকার, ফেসবুকে ম্যাসেজ দাও ঃ<br /><a href=""https://www.facebook.com/shoshi.islam.733"">https://www.facebook.com/shoshi.islam.733</a>",0,entertainment
খুব কষ্ট পায়লাম,0,entertainment
অল দ্যা বেস্ট শাবনূর ম্যাডাম এগিয়ে যান,0,entertainment
আমার সবচেয়েপিয়ো ছবি মনপুরা এইবার দিয়ে ৬বারের মতো দেকলাম,0,entertainment
ইসলাম নিয়া কেউ মজা করার সাহস দেখাবেননা। নাটক সব ঠিক আছে মোনাজাত নিয়া মজা করা ঠিক হয়নি ভবিষ্যৎতে এই গুলা খেয়াল রাখবেন,0,entertainment
তোমারে পুলিশে লইছে কেডায়?🤣🤣,0,entertainment
আরেকটা কথা। বর্তমানে বাংলাদেশে যেসকল অভিনেতা অভিনেত্রী রয়েছে মুলত তারা যতদিন সিনেমা জগতে থাকবে কোনো নতুন প্রতিভাবান চেহারা পাওয়া যাবে না ততদিন অবদি,0,entertainment
"আমি এই ছবিটা দেখে অঝড়ে কেঁদেছি যাদের হাট সমস্যা আছে তাদের বুঁকের ব্যাথা উঠে যাবে আমার ও বুঁকে ব্যাথা শুরু হইছে ,",0,entertainment
মান্নার অভিনীত সিনেমাগুলো অসাধারণ,0,entertainment
দিলদার আমাদের সবার প্রিয়।।দারুন অভিনয়।,0,entertainment
ভাল বাংলা ছবি নাই,0,entertainment
অ প্রত্যাশিত,0,entertainment
তোদেরকে জুতা পিটা করা উচিৎ,0,entertainment
রুবেলের লৌহমানব আর জসিমের ধর্ম আমার মা আপলোডকরবেন প্লিজ।,0,entertainment
ওরে বিস কচু ডুকিয়ে দাও,0,entertainment
ভাই মহিলা হোস্টেল আপডেট দেন প্লিজ,0,entertainment
বাংলাদেশ ইতিহাসের<br />সব থেকে সেরা সিনেমা,0,entertainment
রিয়াজ শাবনুর মানে অসাধারণ কিছু,0,entertainment
ডিপজলের এডাল বই,0,entertainment
ধন্যবাদ গঠনমূলক ভিডিওটা বানানোর জন্য,0,entertainment
আপনারাসবাই সালমানের জন্য দোয়া করবেন আল্লাহ তাকে জানো জানাত বাশি করুন,0,entertainment
মিথিলা ভিতরটা খুবই জঘন্য ।ও কোন পুরুষের সাথেই সুখি হতে পারে না। কারন নিজে সুখী হওয়ার জন্য অন্যকে সুখী করতে হয় সেটা হয়ত মিথিলার জানা নেই। নিগরুদের সোনাটা যদিও অনেক বরো তাদের সাথে ও যদি বিয়া হয় তাহলে সুখী হতে পারবে না।,0,entertainment
একবার মরার কথা চিন্তা করেন।,0,entertainment
অপুকে ভলচি ভেঙিয়ে পঢ়না দেকবা একদি আপনাৰ শাকিব আপনাৰি হবে দুই পিতিবিৰ মত&quot;©,0,entertainment
"যে ভালোবাসা বুঝে না <br />তাকে ভালোবাসা শিখাতে যাবেন না,কারন <br />সে ভালোবাসা শিখবে আপনার কাছে,<br />কিন্ত,ভালোবাসবে অন্য একজন কে, আর কষ্ট পাবেন আপনি, 😥😥🤢🤢",0,entertainment
আমা্র তো খুব ভালো লাগছে,0,entertainment
শাবনূরের ছবি সত্যিই অসাধারণ,0,entertainment
সিনেমাটায় অনেক ছিন এবং গান কাটা।পুরাপুরি দিলে ভালো হতো।সালমানের মুভি বলে কথা।,0,entertainment
শাকিব খান আর তার ডিজিটাল ছবিকে সামনে রেখে মানুষ পস্রাব করে। কোথায় গেল সেই আগের দিনের ছবি গুলো। বিশ্বাস না হওয়ারই কথা। চট্টগ্রামে এমন অনেক জায়গা আছে যেখানে সিনেমার পোস্টার লাগানো হয়। যদিও লোকজন সেখানে পস্রাব করে। তারপরও সেখানে ডিজিটাল ছবির পোস্টার লাগায়। মানুষ তার উপরে ওইটা......করে।,0,entertainment
ভাই খুব ভালো লাগলো ধন্যবাদ ভাই,0,entertainment
রুবেলের ছবি দেওয়া জন্য আবারো আপনাদের ধন্যবাদ,0,entertainment
বলতে সরম লাগে শাবনুর আপু এত স্টার একটা নায়কা আর আবাল মার্কা নায়কের সাথে ছবি করলো,0,entertainment
অনেক দিনপরমুক্তি পেল,0,entertainment
মুরগীর বাচ্চা,0,entertainment
চিতার দেখেছি এরকম দেখিনি খুব ভালো লেগেছে আমি ওর এই ধরনের চিন্তার মুহুত করেছি কিন্তু কি করব বলেন কিছু করার নেই আমরা তো অভিনেতা না আমাদের খুনসুটি নেই তাই বাড়িতে অন্যান্য করি আশা করি ভালো লাগলো পড়ে এই নাম্বারে যোগাযোগ করুন 8145 1 2046নাম্বারে যোগাযোগ যোগাযোগ করুন আমার এই নাম্বারে আপনাকে সহযোগিতা করব কি কি করতে হয়,0,entertainment
"কেউ কাউরে মারে না,,,সত্যি কথাটা । এমন ডিপজল আরো হয়তো হবে কিন্তু এমন অভিনেত্রী হবে না!! সেই সাথে মান্নার মৃত্যুতে আমরা গভীর ভাবে শোকাহত,,,ডিপজলের সু স্বাস্থ্য কামনা করছি,,,সেই সাথে সকল অভিনেত্রী বৃন্দ!!",0,entertainment
আগে ভালো ছিলো এখন কামলা নিতে হবে টিপানের জন্য,0,entertainment
ভালো লাগলে আগেও একবার দেকছি,0,entertainment
ধনী কুকুরদের এ দুনিয়াতে বিচার হয়না। বিচার শুধু গরিবের জন্য। এটাই সমাজ!,0,entertainment
ভালই।। বাট নুসরাতের আরও উন্নতি করতে হবে মনে হয়,0,entertainment
"সত্যই কোনো কথা হবে না,,,<br />Nayeem and Aporna জবাব নেই,,,,",0,entertainment
একদম রাইট আপনার কথা গোলো,0,entertainment
পৃথিবীর সব মানুষ ভালো বাসার কাছে দূর বল,0,entertainment
আইজকা ওয়ে ওয়ে রাইত😂,0,entertainment
এই রকম উল্টো পাল্টা নাইছ গানের মইদ্দে আমি আমার জীবনে ও দেকি নাই হেতে বলে নায়ক,0,entertainment
ভাই এসব ভিডিও বানালে তাহসান ভাই কষ্ট পায়...! লোকটারে মারবেন নাকি আপনারা!!,0,entertainment
নাসরিন এর বেস্ট মুভি এইটা।,0,entertainment
দেখা শুরু করলাম আশা করি ভালো হবে / আর হতে ই হবে বস আছে তো,0,entertainment
ইলিয়াস কাঞ্চনের কোন সিনেমা যে হিট নয় তাই তো জানি না। সব গুলোই হিট। সুপার স্টার নায়ক কাঞ্চন ভাই।,0,entertainment
কি অসাধারন অভিনয় ইলিয়াস কাঞ্চনের মুগ্ধহয়ে গেলাম,0,entertainment
হিমু চরিত্রে একমাত্র রিয়াজকেই মানাবে.....,0,entertainment
শেষের দিকে খুবই দুঃখজনক,0,entertainment
আচতে টিপ,0,entertainment
"ছবিটা প্রথম দেখি ১৯৯৭ সালে,তখন আমি ক্লাস ফাইভ এ পড়ি,অসাধারণ ছবি",0,entertainment
তোকেতো দেখতে চায়না দেখতে চায় তোর বড় দুধ গুলা বুঝিসনা,0,entertainment
এই সিনেমা টা শুধু সাবনূর কে ভালবাসি বলে সিনেমা টা দেখসি...না হয় এইরকমএই রকম সিনেমা বাংলাদেশ ছাড়া কোনো দেশে হয় না....,0,entertainment
খুব ভালো হয়েছে ট্রেইলার টি! দেখেই বোঝা যায় নির্মাণ অসাধারন। গল্পটা খুব ভালো বোঝাই যাচ্ছে। হিরো দেখে ভেবেছিলাম কেমন না কেমন অভিনয় করবে! কিন্তু যতো দেখছি ততোই ভালো লাগছে৷সবমিলিয়ে খুব ভালো লাগলো। সত্যিই বাংলা সিনেমার একটা পরিবর্তন আসতেছে৷ অপেক্ষায় আছি ১৩ সেপ্টেম্বরের। 🙂,0,entertainment
এই ছবির নায়ক ভুবন কেসি(নেপাল) তার এবং আমার জন্মদিন একই দিনে,0,entertainment
এই স্যানেলে পর্নো স্টার জনি সিন্সের একটা রিপোর্ট চাই।,0,entertainment
"আমার সবচেয়ে প্রিয় ছবি ,",0,entertainment
খুবই ভালো লাগলো। শেষে মেয়েটার মারা জাওয়াতে খুবিই ইমোশনাল হলাম। রুবেল ভাই বাংলাদেশের সরবোশ্রেষ্ঠ একশন হিরো এই ছবিটা না দেখলে বুজতাম নাহ। খুবি দারুন একশন ছিল।,0,entertainment
ওনাকে বলুন একটু খুলে দেখাতে।আমরা দেখতে চাই।,0,entertainment
অনেক ধন্যবাদ অনেক দিন ধরে খুজসি 1999সালে দেখসিলাম,0,entertainment
"এইসব জানোয়ার পুরুষদের জন্য আমাদের সমাজ অনেক পিছিয়ে আছে,,,,,, খুব শিক্ষনীয় ভিডিও",0,entertainment
"যে জীবনে কোনদিন না কেঁদেছে সেও কাঁদবে, আর সাবানা একজন কিংবদন্তী",0,entertainment
মুভিটা খারাপ হলেও সংসারের আমার খুব ভালো লেগেছে,0,entertainment
পরবর্তি পর্ব চাই,0,entertainment
খুবিই সুন্দর লাগছে নাটকের কাহিনীটা,0,entertainment
ভাই লজ্জাহীন মেয়েটাকে নিয়ে প্রোগ্রাম করা উচিত হয়নি।।।। আপনার আত্মসম্মান বিযয়টিকে ভাবা উচিত।।।।,0,entertainment
"খুব ভাল ছায়াছবি, খুব ভাল লেগেছে। ধন্যবাদ এই ছবির কলা কসুলি ও পরিচালক দেলোয়ার জাহান ঝন্টুকে",0,entertainment
ছবি হোক ছবির মতো আমরা চাই এরকম ছবি আবার আসুক বাংলাদেশ চলচ্চিত্রের মাঝে,0,entertainment
বালের রিয়েলিটি শো শালারা সবাই আবালের দল পাগলের মতো দলবেঁধে ছুটছে মাসুদ রানা হতে,0,entertainment
ভালো নায়কা না হলে গান কি আর ভালো লাগে,0,entertainment
কোন মেয়েই নিজ ইচ্ছাই পতিতাই লিপ্ত হয় না,0,entertainment
পোড়ি বেস টা সুন্দর না Trailer দেখে মোটামুটি সরিলটা ভাভআসছে না কোনো হৈ চৈ আছে 😂😂,0,entertainment
খালিদ হাসান মিলুর কন্ঠে দিলদারের মুখে সত্যি অসাধারন।,0,entertainment
নায়কের জন্য ছবিটা পুরো দেখার ইচ্ছে হলো না,0,entertainment
এর চেয়ে মরন অনেক ভালো,0,entertainment
পিল্জ এই ছবির সব গান আপলোড দিন,0,entertainment
"আন্তর্জাতিক মানের একটি মিউজিক কম্পোনেন্ট,বাজে ড্যান্স পারফর্মেন্স ও ব্যাকগ্রাউন্দের জন্য সম্পূর্ণ লোকাল হয়ে গেলো।",0,entertainment
আমার চ্যানেলেও ভরছি ভালা মত।,0,entertainment
ইলিয়াস কাঞ্চন অভিনিত শিবা গুন্ডা বাংলা মুভি টি আপলোড দিবেন প্লিজ।,0,entertainment
অ্যাকশন মানি রুবেল,0,entertainment
খুব ভাল হইছে,0,entertainment
এই ভাই দেখতে হবেনা নায়ক কার প্রিয় শাকিব খান আমার প্রাণ প্রিয় নয়ক।,0,entertainment
রিয়াজ ভাই অভিনয় করলে মনেই হয় না অভিনয়,0,entertainment
দুনিয়াতে এইরকম মানুষ আছে আল্লাহ আমাকে উঠাইয়া নাও। দুধু দেখাইতে এতো আয়োজন। গজব পরবে তোর দুধের উপরে,0,entertainment
আমার ধোন টা কেঁপে কেঁপে কাদঁতে শুরু করেদিলো ।,0,entertainment
এক কথায় অতুলনীয়!!!!,0,entertainment
এই মাস্টারপিস মুভিতেও যারা আনলাইক দিছে তারা কারা???!!,0,entertainment
অভদ্র প্রেম এ বাংগালীরা গালি দেই কিন্তু এই নায়িকার পোশাকে সবাই বাহ বাহ দিচ্ছে! এটাও তো বাংলাতে চলেনা! আরে ভাই ভালো হইলে সব ক্ষেত্রে হ!,0,entertainment
কি বলিবো ভাই কি ভাভে ধন্যবাদ দিবো বলার ভাসানাই,0,entertainment
থাপ্পড় দেওয়া দরকার দাঁড়িওয়ালাকে বেয়াদ্দব,0,entertainment
ছবির উক্তিগুলা বাস্তব।<br />কোটা পদ্ধতির জন্য।<br />অনেক মেধাবী চাকরি পাচ্ছে না।,0,entertainment
ভাইয়া মায়ের জন্য যুদ্ধ মুভিটা আপলোড দেন না প্লিজ ভাইয়া প্লিজ দেন প্লিজ,0,entertainment
মুভিটা খুব সুন্দর আমার পছন্দ হলো,0,entertainment
আমার ইচছা করেনা নাটক,0,entertainment
তুই আমার,0,entertainment
আমি ও একজন কে ভীষণ ভালবাসি,0,entertainment
বাংলাদেশের শেরা ছবি,0,entertainment
এই নদীতে যদি একবার গোসল করে পারতাম মনে অনেক আনন্দ পেতাম যারা যারা এই নদিতে গোসল করতে চাও তাহলে চলে আসো এই বাংলোতে। এরকম হট মুভি দেখা যাচ্ছে না আগের মতো।,0,entertainment
যারা এইভাবে মারছে তারা মানুষের বাচ্চা না অমানুষের বাচ্চা আগে যানার উচিত ছিল মেয়েটি কেনো আসলো,0,entertainment
বাংলাদেশের মধ্যে মান্নার মতন নায়ক আর হবে না আর কেউ হতে পারবে না,0,entertainment
আমার কাছে ওনেক ভালো লাগছে গানটা বছিটা জানি কেমন হবে,0,entertainment
ছেলেটাকে ঠকানো উচিত হয় নি মেয়েটির,0,entertainment
অনেক সুন্দর হয়েছে নাইচ মুভি টা আমার,0,entertainment
সেই ছবি ভাই,0,entertainment
আমাদের দেশের পরিচালক গুলো মদ পান করে ছবি নকল করে এক রকম ছবি কয়টা দূর শালা পরিচালক,0,entertainment
নতুন পর্ব আপলোড করার জন্য থ্যাংক ইউ,0,entertainment
নায়েচ,0,entertainment
"খুব ছোট কালে ছবিটি দেখে ছিলাম,<br />আবার ২০/৮ ২০১৯ দেখলাম, খুব ভালো লাগলো",0,entertainment
আমরাই যথেষ্ট পাপী আর তুই মরলে যে কি হবে 😡😡,0,entertainment
লিজার কয়েকটা ছবির নাম বলেন,0,entertainment
মম ব্রাহ্মণবাড়িয়ার মেয়ে তো তাই একটু বেশি নেকামি করে,0,entertainment
আমি কি বলবো বুঝতে পারছি না 😅😅ভাষা হারিয়ে ফেলেছি ।Prince soriful rajbari. pori.6.8.2019.,0,entertainment
সেই বাংলাদেশের নাটক আরো চাই😆😆😆😆😉😉😉😉😉😉,0,entertainment
আর হাশতে হাশতে আমাগো বুক বেথা করতেছে,0,entertainment
কি নাটক ছিল আগের দিনের! আর এখনকার নাটকের কথা আর বললাম না।,0,entertainment
"অসাধারণ জাকা নাকা একটা ছবি দেখে অনেক ভালো লাগছিল,, এবং সুপারহিট আলেকজান্ডারের পাওয়ার সবগুলো শাকিব খান শিখে নিয়েছে",0,entertainment
আশাকরি অনেক সুন্দর একটা কাহিনী খুব মজার একটা ছবি হবে।,0,entertainment
"কি অসাধারণ বাংলা সিনেমা,বারবার দেখলেও মন ভরে না,",0,entertainment
অনেক অনেক সুন্দর লাকছে,0,entertainment
নাটকটি কষ্টের হলেও অভিনয় গুলোকে চমৎকার না বলে উপায় নেই।,0,entertainment
এই বইয়ের মিল ঠিক ঠাক হয়নি যখন ভোটার লিস্ট জন্য জিজ্ঞাসা হচ্ছে ছিল বাদ চলে গেল কেন আশা কখন মারা গেল,0,entertainment
"গানের প্রিন্ট গুলো বাজে, দয়া করে কিছুটা হলেও ভাল করবেন প্লিজ?",0,entertainment
আমার জীবনের সেরা সিনেমা এইটি,0,entertainment
সানাই এক খারাপ মেয়ে,0,entertainment
"নাটকে কিছু কিছু সময় মেহেজাবিন এর কন্ঠ অন্য কারো দেয়া মনে হলো,,,,নাটক টি সুন্দর ছিলো!!",0,entertainment
পাগলের মতো দারি আবাল বিচারক,0,entertainment
আমার জীবনটার সাথে 100% মিল..,0,entertainment
এই।গরু ছবি কেও।দেখে।ছি ছিএকি।একটা নায়ক হলো ছাগল দিয়ে হাল চাষ করেমানুষ জন কি।যে।রুচির,0,entertainment
বক্সিগো 😂😂,0,entertainment
"এই ছবিতে অভিনয় করছিলেন জননন্দিত সালমান শাহ অভিনীত সিনেমা কিন্তু পরিপূর্ণভাবে সম্পূর্ণ শুটিং শেষ করতে পারে নাই ৫০ ভাগ সে অভিনয় করছিলেন কিন্তু দুর্ভাগ্য এই ছবির পরিচালক কর্তৃপক্ষ পরে নতুনভাবে হুবহু ওমর সানী কে দিয়ে করানো হয় <br />চরম দুর্ভাগ্য যে জননন্দিত নায়ক সালমান শাহ ছবিটি শেষ করার পূর্বে সালমান শাহ পরলোকগমন করেন কিছু দুষ্কৃতকারীদের হাতে অকালে প্রাণ ঝরে যায় এই জননন্দিত নায়ক সালমান শাহ এর <br />তার জীবদ্দশায় রেখে যাওয়াসাইনিং করা প্রায় ৫০ টি ছবি পরবর্তী সময়ে নবাগত নায়ক রিয়াজ কে ও ফেরদৌস ও ওমর সানী মান্না কে দিয়ে ছবি বানানো হয়েছে<br />সালমান শাহ অভিনীত সাইনিং করা ৫০ টি ছবির নায়িকা নির্বাচিত হয়েছিল পপি, শাবনূর, বৃষ্টি, পূর্ণিমা ,শাবনাজ , মৌসুমী এরকম অভিনেত্রী শিল্পী ছিল তার সহনায়িকা <br />ইতিহাস সম্পূর্ণ চির সত্য",0,entertainment
খুব সুন্দর বই,0,entertainment
ছবির নাম কি দাদারা,0,entertainment
ভাই প্রত্যয় হিরন এর ভিডিও কবে আসবে প্লিজ বলেন না,0,entertainment
কতা একটাই বস,0,entertainment
ফালতু জাজ আচরণ গুলা,0,entertainment
খুবভালো একটা ছবি,0,entertainment
কবির কাঙ্কাল না দিয়ে মুন্সিপাটি ভালো হইতো,0,entertainment
অনন্তের ছ এর উচ্চারণে ঝামেলা আছে,0,entertainment
"ওনেক সুন্দরমুভি, মিচ করবো আবার,সাবনুর, রিয়াজ ভায়া।",0,entertainment
"ভালো লাগলো,যে নাটকে ও ভূতের কাহিনী আছে যা আমরা দেখতে পারবো",0,entertainment
সানাই তুই সেক্সি মাল,0,entertainment
খুব সুন্দর একটা ছবি দারুন,0,entertainment
বছরের প্রথম দামাকা,0,entertainment
এই ধরনের মেয়ে কে দেখাও পাপ আল্লাহর ভয় তার মনে নেই মরার পর কি যে হবে তার তখন বোঝবে কি করছে সে,0,entertainment
হি,0,entertainment
আপনাকে অশঙ্খ ধন্যবাদ এত সুন্দর বাবে গুচিয়ে এই ঘটনা বলার জন্য।,0,entertainment
শুরুতে ই হাসির জুড়ি--অনেক সুন্দর হয়েছে,0,entertainment
"এরকম ছবির সাথে বাস্তব জিবনের সাথে কাহিনি মিলে যায়,ছবি দেখার পর আবেক মনকে বোঝাতে পারি না",0,entertainment
মেয়েদেৱ কাছে সত্য কথাৱ মূল্য দেতে জানে না,0,entertainment
শেষ ভালো যার সব ভালো তার। nice natok,0,entertainment
"নতুন কোন কিছুই সহজে নিতে পারিনা আমরা,",0,entertainment
অপূর্বর কনঠর সুর সব নায়ের চেয়ে সুন্দর কনঠ গলার ভয়েজ অসাদার একটিম বলার ভাষা বলে বুজানো সমভব নয়,0,entertainment
এমন শাসারি কার ভাগ্য যেনো না জটে,0,entertainment
"কারো জীবনের অতীত, আবার হয়তো কারো জন্য ভবিষ্যৎ এর অপেক্ষা এই গল্পের মতোন পরিস্থিতি,হয়তো মিলনটাই হয় বা হয়না",0,entertainment
পাবনা থেকে কি ভাবে ছাড়া পেল এরা,0,entertainment
দু খালাই এক আবার সানাইয়ের মুখে আল্লাহর নাম!! এসবের ইন্টারভিউ নেওয়া মানুষ গুলোও ওদের কলেটি,0,entertainment
"আগেই বলছিলাম নিলয় ফিলয় রে বিয়া করার দরকার নাই,,, আমি তো আছি, নাকি",0,entertainment
বালের ডাইলগ।<br />বস্তি মার্কা,0,entertainment
এটা কিছু হইলো!!! 😜😜😜,0,entertainment
এই ছবিরএকটা গান আছে। কারে বলি মনেরব্যাথা। কানটি কই ভাই,0,entertainment
এরা বিচারক হওয়ার কোন যোগ্যতা নাই,0,entertainment
আমি কি দিয়ে ধন্যবাদ জানাবো সেই ভাষাটাই হারিয়ে ফেলেছি,0,entertainment
বেস্ট হিরো আরফিন শুভ,0,entertainment
এই ভিডিও টা দেখে আমি আপনার ফ্যান হয়ে গেলাম। আমি অনেক ভিডিও দেখছি। কোনো দিন কমেন্ট করি নাই। এই প্রথম কমেন্ট করলাম। লাইক করলাম। আই লাইক ইউ। আমার খুব ভাল লাগলো।,0,entertainment
"মেগাস্টার রুবেল,,পাশাপাশি নায়িকা,, মিশেলা অসাধারণ মারপিট গুলো,,,",0,entertainment
তুর্কিরা এটিএন নিউজ দেখে।। 😅😅😅,0,entertainment
গরিবের মিয়া খলিফা। নিজ তালা ভারা দিয়ে দুতালা বানায় 👉👌,0,entertainment
হাহাহাহা হালা কয় কি একটা বাচ্চা হওয়ার পরেও ভার্জিন থাকে কি করে,0,entertainment
সাকিব হলো সুপার হিরো,0,entertainment
কিং খান আমার নাম,0,entertainment
কের সাকিব রিয়াজের সামনে তার টাইম নাই সে-তো রিয়াজের সাথে যতগুলো মুভিতে অভিনয় করলেন তাতো সেকাই খাইলো <br />রিয়াজের সাথে কোনো তোলনাই নাই,0,entertainment
অপূর্ব এরকম একটা বাজে নাটক করবে আমি না confessedশুধু সময় নষ্ট করলাম,0,entertainment
যারা বিচারক তারাইবা কতটুকু যোগ্য!!!,0,entertainment
আমিন খান কি শুধু নামেই আছে?,0,entertainment
সালা গো আর কোন কাজ নাই মনে হয় 😔বাংলাদেশেরে কি ভাবে নিচে নামাবে সেই চিন্তায় থাকে,0,entertainment
গান টা ভালো কিন্তু যে গাইছে তার কন্ঠ ভালো না।,0,entertainment
মিথিলা শুধু ভোগের পন্য হয়ে গেল,0,entertainment
আমার সোনার ছবি করে বাপ্পি আমার সোনার নাইক1,0,entertainment
ভিডিও টি ভালো লাগলে লাইক ও শেয়ার করুন এবং সাবস্ক্রাইব করে রাখুন। আপনার মতামত কমেন্টে জানান। ধন্যবাদ,0,entertainment
যত সব ফালতু এতে কিছুই শেখার নেই,0,entertainment
সচেতন মুলক নাটক।,0,entertainment
অস্থির ভাই কোন কথা হবে না😍,0,entertainment
চরম নাটক,0,entertainment
আমি আছি,0,entertainment
আবরার হত্যার বিচার চাই হত্যাকারীদের ফাঁসি চাই,0,entertainment
সেই মুহূর্ত যখন সারারাত গঞ্জিকা খেয়ে কেউ লিরিক্স লেখতে বসে!,0,entertainment
আমার মনে হয় যারা এই মুভিটিতে অভিনয় করেছিলেনতারা সবাই জনগণের মার খাওয়ার ভয়ে বোরকা পরে রাস্তায় চলাফেরা করে 🤣🤣🤣🤣🤣🤣 পরিচালক কে অস্কার পুরস্কার দেওয়া দরকার 🤣🤣🤣🤣,0,entertainment
ধুকখলাগে,0,entertainment
ছুপার মুভি,0,entertainment
আমার চেনেলটি গুরে আসুন নুতুন গান,0,entertainment
প্রতিদিন সিরিয়াল গুলো ঠিক মত দিলে সাবস্ক্রাইব করবো না হয় করবো না।,0,entertainment
খুবই সুন্দর আরো ভিডিও চাইআপনার চ্যানেল থেকে ।,0,entertainment
বাংলায় এখন কি এমন মানুষ আছে,0,entertainment
"নাটক দেখতাম কিন্তু বাদ দিয়েছি দেখা, কারন হলো, তার বউকে দেখে মেজাজ খারাপ হয়ে গেছে",0,entertainment
ভিতর টা কেমন জানি কাঁপন অনুভব করলাম।,0,entertainment
তাসিন ভাই আপনি আমাদের মত মানুষদের মনের কথাই বলেন ধন্যবাদ।,0,entertainment
ফুলমবি আপলোড দিন নাহলে অনেকে বাজেমন্তব্য লিকে কমেন করে,0,entertainment
পুরান নাটক তো ভাইয়া নতুন নাটক আপলোট দেন,0,entertainment
আসসালামুয়ালাইকুম আমার নাম মোঃ জুয়েল ভাই আমি একটা প্রতিবন্ধী ছেলে লটারি পেতে গেলে ভাগ্য লাগে তেমনি করে আপনাকে আপনার দেখা পেতে ভাগ্য লাগে কিন্তু আমি রাগ করবো সারাক্ষণ আমি আপনার কাছে মেসেজ লিখে দেবো কিন্তু দেখি আপনি আমার মেসেজটা কবে পড়েন ভাই আপনারা করবেন আপনি কি আমার কথা একটু বলবেন আপনার সাথে একটু দেখা করতে চাই 01788560904,0,entertainment
ফালতু নায়কের ফালতু মুভি,0,entertainment
মহানায়ক তুমি মান্না ভাই,0,entertainment
"থ্যাংকস ভাই,যদি পারেন, বিশ্বপ্রমিক ছবিটা দিন।",0,entertainment
"আমাদের দেশের মত কোন দেশের রুপ এমন সুন্দর বলেন,,চকচক করলে যেমন সোনা হয়না,, তেমনপাকা রাস্তা ঘাট হলেই সুন্দর মনের মত দেশ হয় না,,,আমি তোমার মুগ্ধময়ী রুপে অন্ধ দেশ আমার দেশ... 😊😍❤",0,entertainment
জলিল ভাই কেমন আছ,0,entertainment
নষ্টামিকে বেশী প্রাধাণ্য......,0,entertainment
জু লি বিচারক,0,entertainment
জাফর ইকবালের মাস্তান ছবিটা আপলোড করবেন প্লিজ,0,entertainment
এই রকম মেয়েদের স্বপ্ন বাস্তবায়ন করা আমাদের সবার কতব্য ভিডিও টি খুব ভালো লাগলো,0,entertainment
মামা ভালই বলছো,0,entertainment
"রিয়াজ ভক্তরা কই সবাই সাড়া দাও,<br />রিয়াদ ভাইকে আবার রঙিন পর্দায় দেখতে চাই",0,entertainment
পুরাই খারাপ একটা মেয়ে,0,entertainment
ছবিটার নাম কী,0,entertainment
পতিতাকে নিয়ে টিভিতে আসাঠিক না।,0,entertainment
মটো সিদ্দিক এর জায়গায় মোশারফ করিম কে দিয়ে করানো হলে ভালো হতো।,0,entertainment
মনের অজান্তে কান্না চলে আসল।।,0,entertainment
গল্পটি অনেক সুন্দর হইছে। শেষ দৃশ্যে কান্না চলে আসল।,0,entertainment
কস্টের কারাগার..,0,entertainment
"খালেদা তো অস্তির কথা কইছে, ২ তিনটা যে উলাইছো,, হাহাহাহাহা",0,entertainment
পুরা মুভি আপলোড করেন।,0,entertainment
ইসলাম ধর্ম সম্পর্কে আপনার কোনো ধারনা আছে পরিচালক সাহেব।,0,entertainment
যারা ভালো কাজ করে আল্লাহ তাদেরকে ভালবাসেন তাদের জন্য উত্তম প্রতিদান দিবেন,0,entertainment
সাকিব শাবনূর আপু দারুন সুপার অভিনয় করছেন ধন্যবাদ সাকিব শাবনূর আপু কে,0,entertainment
সিলেটী ভাষায় নাটক করাইতে অইলে সিলেটী মানুষ ছাড়া সম্ভব নায়। সুতরাং ইলা ফাউল নাটক বানাইয়া লাভ নাই। মোশারফ করিম সব ভাষায় কথা খইত ফারে বাট সিলেটী ভাষাত আইয়া লাড্ডু।ফরবর্তিতে সিলেটী ভাষায় নাটখ বানাইলে সিলেটী অভিনেতা-নেত্রিরে দিয়া বানাইবা। আন্নায় সিলেটী ভাষায় নাটক বানানির কুন দরখার নাই।,0,entertainment
বুম্বা দা সেরা অভিনেতা.....😍😍,0,entertainment
জাকির ইরাকের বসরা শহর থেকে ।,0,entertainment
আজ রাতে হাত মারতে হবে,0,entertainment
এতো সুন্দর একটা গানের সাথে মেয়েটির ড্রেস একটুও ঠিক হ্য়নি তাই পছন্দ করলাম না,0,entertainment
অনেক বার দেখছি তাও বারবার দেখতে ইচ্ছে করে,0,entertainment
নাটকটা সত্যিই চোখে পানি চলে আসে দেখলে ইউ টিউব এ দিলে আরো অনেক বার দেখতাম প্লিজইউ টিউবয়ে ছারেন,0,entertainment
তোর চেহারা দেখলে আমার রাগ উঠে 😡😡😠😠😈😈সালা,0,entertainment
ধন্যবাদ জানাই পরিচালকে এরকম শর্ট-ফিল্ম তৈরী করার জন্য,0,entertainment
এদরনেন ভালো ছবি আমরা আর কি পাবো,0,entertainment
সেরা ছবি ভালো লাগে,0,entertainment
"বড়ো লোকের বা ধনীদের নাটক দেখতে ভালো লাগে না- মন খারাপ ছিলো।<br />তাই, আজ মন চাই হলো-<br />গরীবের নাটক দেখি, মনটা শান্তি ও ছবর আসবে-- এখানেও মিথ্যা-- চোরি- মায়ের বুক খালি।<br />আল্লাহ! বলেন- গরীবরা জান্নাতে প্রথম যাবে-।।",0,entertainment
আরো হট ছবি দেন🔞🔞🔞,0,entertainment
ইউসুফ জুলেখার পর্ব গুলো অনেক ভালো ছিলো,0,entertainment
"সবাইকে অনেক অনেক ধন্যবাদ , বাংলা নাটক দেখার জন্য ।",0,entertainment
রুবেলের ছবি আরো চাই,0,entertainment
অনেক দিন পর দেখলাম,0,entertainment
ভাই পাগাল হয়ে যাই এই নাটক টা দেখলে।,0,entertainment
আমার মাথা ফেটে গেছে সাথে আমার স্যাটেলাইট ও দাঁড়াইয়া গেছে 😂,0,entertainment
মান্নার উল্টাপাল্টা/ প্রসেনজিৎ এর বিক্রমসিংহ / অক্ষয়েরও সিনেমা রয়েছে এটা।মান্নার সিনেমা থাকার পরও কপি আবারও সেই বাংলা সিনেমাই।বালের বাংলা ফিল্ম,0,entertainment
বাপের টাকা মুভি চাই।,0,entertainment
সালমাম শাহ এর মত নায়ক নাই আর হবেও না,0,entertainment
অার কোনো দিন মান্না ভাইয়ের মতো নায়ক বাংলাদেশে হবে স্যালুট মান্না ভাইতুমি হাজার মানুষের বিরে বেচে থাকবে ভাই? মান্না ভাইয়ের গারতি পুরুন হবে না,0,entertainment
হুম অসাধারণ একটি রোমান্টিক গান,0,entertainment
আগের পরিচালকে বাংলা মুভি গুলো পরিবার নিয়ে দেখা যেতো এখন আর পরিবার নিয়ে দেখা মতো পরিবেশ নাই,0,entertainment
"আমার প্রিয়,বাপ্পারাজ।",0,entertainment
প্রিয় নায়িকার গানটা প্রিয়।💞💞💞,0,entertainment
কি মুভি দিলিরে ভাই,0,entertainment
দিয়াশালাই দেখলে বুঝা যায় সানাই কেমন অভিনেত্রী ৷ছি ছি ছি থু৷,0,entertainment
সত্যি খুব ভালো লেগেছে ছবিটা যত ছবি দেখেছি তার মধ্যে এটাই সেরা ছবি এই ছবিটি এত ভালো লেগেছে যে তিন বার দেখেছি তবে খুব কষ্ট লেগেছে বিশালের জন্য,0,entertainment
এ নিয়ে তিন বার দেখলাম,0,entertainment
নাউজুবিল্লাহ অাল্লাহ মাফ করুক,0,entertainment
"ওরে সাকিব তোর অপুকে আপন করে নে,,,",0,entertainment
"ছবির নাম দেখে মনে হইসে,,,ছবির পরিচালক বস্তি এলাকার বাসিন্দা",0,entertainment
পরবর্তী পর্ব,0,entertainment
আসলে একটা মেয়ে কে নষ্ট করে কিছু মানুষ নামের পশুরা,0,entertainment
"অনেক ধন্যবাদ পর্ব দুই দেওয়ার জন্য,, খুব ভালো লেগেছে নাটক টা ।।👏👏👏",0,entertainment
এগুলা হাইস্সকর হাইস্সকর,0,entertainment
রিয়াজ শাবনুর এর মুভি দেখলে সত্যিই নিজেকে ধরে রাখা খুব কষ্ট হয়। তাদের অভিনয় দেখলে অভিনয় মনে হয়না কোথায় যেন হারিয়ে যাই,0,entertainment
ভাই অন্যান্য ভিডিও আপ না দিয়ে জান্নাত আপ দেন। তাতে করে সাস্ক্রাইব কমবে না বরং বাড়বে ওকে,0,entertainment
"রুবেলের, ইনকিলাব, মালামাল, অন্যায় অত্যাছার, আন, ,,,,,, ছবিগুলো আপলোড দিবেন প্লিজ।",0,entertainment
যাদেরকে অপমান করা হয়েছে তারা সবাই এক হয়ে মামলা করেন ভাইসব।,0,entertainment
এই রকম দেখতে চাই,0,entertainment
সন্ত্রাস মুভি টা যত বার দেখেছি ততো ভাল লেগেছে সত্যি অসাধারণ একটা মুভি. বাংলা অ্যাকশন মুভিতে রুবেলের অবদান কোনোদিন মুছে ফেলা যাবে না. Rubel is the most wonderful action hero in bangla film industries.,0,entertainment
কিরে হিন্দু বাড়িতে আল্লাহর নাম 😁,0,entertainment
"এটাই বাস্তব কাহিনী,,",0,entertainment
মোসারফ করিম বেস্ট,0,entertainment
তুমি দিওনা গো বাসর ঘরে,0,entertainment
তাহসান এর সাথে সাবিলা বাচ্চা যায় না,0,entertainment
শাকিব খান ও ফারিয়া ফাটিয়ে দিলেন,0,entertainment
সাকিবের বক্তরা হাত উঠাও,0,entertainment
"দেখতেছি আর চোখের পানি মুছতেছি সত্যি অসাধারণ ০৬,৯,২০১৯। আর কে কে আছেন লাইক দিয়ে জানিয়ে দাও",0,entertainment
জাপর ইকবাল স্যারের লেখা বইয়েরবক্ত কে কে 😎😎😎😎😎😎😎😎😎😎,0,entertainment
অনেক খুশি হব।<br />ফুল ছবি দেন<br />আমি গুন্ডা আমি মাস্তান এবং<br />কিলার গান এবং হট সিন সহ<br />প্লিজ প্লিজ প্লিজ,0,entertainment
ভাইয়া ভিডিও টা অনেক ভালো লাগছে...??,0,entertainment
হুমায়রা হিমুর বাবা যে লোকটা উনাকে একদম মানায় নি এইসব নাটকে।কি একদম ঘাদার মতো একটা লোক নিয়েছে পরিচালক।,0,entertainment
হুমায়ূন ফরিদী অভিনয় অসাধারণ ।,0,entertainment
ময়দার বস্তা নায়িকা,0,entertainment
আর এপিসোড গুলো কবে দেবেন ??? can&#39;т waιт 😣😣😣😣😣,0,entertainment
অনেক আগের ফিল্ম তো এই কারনে <br />সাউন্ড কোয়ালিটি ভালো না <br />কিন্তু অভিনয় এন্ড কাহিনি <br />সবই ভালোহইছে,0,entertainment
দেশে কী ছেলেদের অভাব তারা টাকা ছাড়াই ইনসি দুধ করে দিতো,0,entertainment
এই ঘর এই সংসার সিনেমাটা যতবার দেখি ততবারই যেনো মনে হয় প্রথম দেখছি। অসাধারণ। ধন্যবাদ মালেক আফসারিকে।,0,entertainment
"আমার গলার হার খুলেনে ওগো ললিতে, গানটা খুব সুন্দর",0,entertainment
নতূনছবিছাই,0,entertainment
নাটক টা হয়তো আমার লাইফ থেকেই নেয়া হয়েছে........,0,entertainment
খুব ভাল একটা মুভি হবে আশা করি,0,entertainment
সাহরিয়ার ভাই আপনাকে ধন্যবাদ সওি কথা বলার জন্য,0,entertainment
শবনম ফারিয়া ত সংকর জাতের মোটা তাজা দুটি ওলান যাহা পুষ্টি কর☺,0,entertainment
মিনিটে ভিউ ! মিনিটে হাজারেরও বেশী ভিউ! 😳😳😳,0,entertainment
এসব মেয়ে দের কে গিনা করতে হয়,0,entertainment
মেলিসা যে ফাইজলামি করছে তা ধরা খাবে কখন,0,entertainment
সঠিক সিদ্ধান্তের জন্য অনেক ধন্যবাদ। যা হোক নাটক খুব ভালো লাগলো। ধন্যবাদ।,0,entertainment
সবটুকু মন দিয়ে দেখলাম। দারুন হয়েছে। শেষ টা অসাধারন। মিথিলা মিথিলা বলে যখন বাবা চিৎকার করছে। ও জমে ক্ষীর।,0,entertainment
শাবনূর আপুর জন্য ছবি দেখা শাবনূর সবার সাথেই মানায় শাবনূর একজন শক্তি শালী অসাধারণ অভিনেত্রী যার সাথে কারো তুলনা হয় না শাবনূর সর্বকালের সেরা ছিল আছে এবং থাকবে শাবনূর বাংলাদেশের নামবার 1 শাবনূর আপুর নতুন ছবি চাই শাকিব খান হলে আরো ভালো হতো শাবনূর ও শাকিব সর্বকালের সেরা হিট ও রোমান্টিক জুটি আমরা শাবনূর ও শাকিব খানের নতুন ছবি দেখতে চাই,0,entertainment
খুব সুদর্শন ছবি।,0,entertainment
আফ্রিদি যে কয়টা বিডিও দেখেছি ওমন কনো আহামরী লাগে নী কিন্তু এই নাটকের ট্রাইলার টা খুবি সুন্দর ছিল আর ও চিল্লা চিল্লি করে নী অভার ইস্মাট হয়নি একদম একুরেট ছিল এক সময় অনেক দূর যাবে এত দূর যাব্ব যেটা আফ্রিদি নিজেও জানে না জাই হোক বাংলাদেশে এক নাম্বার you tuber,0,entertainment
"অনেক সুন্দর ভাই,, আমি আপনার চ্যানেলটি সাবস্কাইব করে দিলাম,, আপনি আমার চ্যানেলটি সাবস্কাইব করেন।",0,entertainment
সত্যি পুরোনো মুভি গুলো এতো ভালো লাগে কেনো,0,entertainment
বিশ্বাস করেন ভাই..! এই যন্ত্রণার মাঝেও একটা শান্তি আছে..!,0,entertainment
গরুর হাটে কি আবার পাদানি খায়বা ভাইয়া😂😂,0,entertainment
গাজাখোর বিচারক তর চুলের অবস্থথা দেখ তার পরে পরের বিচার করিছ।,0,entertainment
গরীবের ভাবি সকলের বৌ - আদিম ব্যাবসার ঘৃণিত পথ ভবিষ্যৎ প্রজন্মকে অন্ধকারে ঠেলে দেওয়ার হাতছানি।,0,entertainment
মোশাররফ একটা বাজে অভিনেতা কথা বেশি বলে বেশি একটিং করে ও একটা ফালতু।,0,entertainment
দুদু র খূব ছোটো,0,entertainment
আপনাদের ভালোবাসা আমাদের অনুপ্রেরণা। <br />আপনাদের অনেক সাপোর্ট প্রয়োজন।,0,entertainment
ধানমন্ডি লেকের কোনায় চটপটি আর ফুচকা খাওয়া নাটক বানানো বাঙাল্ পরিচালক বানাবে মাসুদ রানা!! শুইনা আমার হাগা ধইরে গেল,0,entertainment
"পরিচালক,, ভাই,,, মুভির কাহিনি বারান সময় বেশি আর",0,entertainment
"শাবনূর আপু আপনি আর নতুন নতুন ছবি করেন প্লিজ প্লিজ,,,,,,,,,,",0,entertainment
ভাই আপনার প্রতি অনুরোধ রইলো এই শ্রেণীর কোন কাওকে আর আপনার শোতে আইনা ফেমাস বানাইয়েন না।যেমন হিরো আলম ও সানাই,0,entertainment
আমি তো কুকটিভিতে 155 নাটক পর্ব দেখেছি আর কোন পর্ব আপলোড দেন না কেন আপনারা,0,entertainment
হাসতে হাসতে মইরা জামু 😂😂😂,0,entertainment
এবার সব গুলোকে জুতা মারা শুরু 😂 😍,0,entertainment
সালমান শাহ্ র গাঁন দেন।,0,entertainment
<b>ধুরু বাল**জুই নামক অভিশাপ টাকে দেখলে নাটক দেখার ইচ্ছা মরে ছারখার তচনচ হয়ে যায়।</b>,0,entertainment
আবালনী একটা😂 ভাইরাল হওয়া জন্য কি না করতে পারে ।,0,entertainment
অনেক কস্ট লাগে তখন যখন মনে পরে সালমান নেই।I misu সালমান,0,entertainment
অর্থের শূন্যতার চেয়েও প্রিয়জনের শূন্যতা অন্তরে ভালোবাসা সম্পন্ন বেশী কাঁদায়।<br /><br />প্রবাসী হলে অনুভব বেশি করা যায়।,0,entertainment
আমরা এখন যা দেখি তা হইলে তা কি?,0,entertainment
বরিশালের ভাষার সাথে কোনো মিল নেই,0,entertainment
গাঞ্জা খোর বিচারক আয়নায় নিজেরে দেকছোস,0,entertainment
এটা মানুষের বিচার নয় অমানুষের বিচার 😭😭,0,entertainment
শাবনূর মানেই বেস্ট 😘😘😘,0,entertainment
শোন তোদের কে বলছি তোরা আগে মুখের ভাষা ঠিক কর তার পরে বিচারক হবি।।।।,0,entertainment
খুব সুন্দর ছবি এমোন ছবি মনে হয় আর হবেনা,0,entertainment
আমি মো জুয়েল রানা আমার জেলা বরিশাল থানা মুলাদি আমি একটা সুন্দর মনের মানুষ চাই,0,entertainment
ভাই পর্ব গোলা শেষ করেন,0,entertainment
হায়রে বাংলাদেশ যেখানে ছোট ছোট বাচ্চা মেয়ে দর্শিত হয় আর সানাই ফারিয়ার মতন মেয়ে ভালোই চলতে পারে তদেরকে ধিক্কার জানাই।,0,entertainment
এটা কোন ধরনের নাটক,0,entertainment
নিচ তলা ভাড়া হবে 🤓🤓🤓,0,entertainment
মনজু একজ পাগল নহে,0,entertainment
আফরান নিশো আর মেহজাবিন চৌধুরী অভিনয় করলে নাটকটা বেশি সুন্দর হতো।,0,entertainment
সুন্দর মুভি,0,entertainment
যারা গেইম পাগল তারা এইখানে আসো লগোতে ক্লিক করে <br />আর সাব করো,0,entertainment
"দেশে কি নায়িকার অভাবপরছে, পরিচালক ভাই,,,যে কোন একটা দিক ত আর্টিস্টদের থাকে,নায়িকার কোন একটা দিক ত ভাল মনে হয় না,,টাকায় যখন খরচ করবেন ভাল একটা নায়িকা নেন,,।",0,entertainment
মেলিসা মনে হয় হিন্দি সিরিয়ালের ফ্যান😂,0,entertainment
পুরাতন খুবই ভালো লাগে,0,entertainment
মদন মার্কা নায়ক।বালের সিনেমা।,0,entertainment
সুন্দর জুটি।,0,entertainment
কাহিনী কি রে ভাই আগের মত জান্নাত বেশি আপলোড দেন না কি হইছে সমস্যা কি,0,entertainment
"এমন ছবি ভালো লাগে,কিনতু কাহিনী ছারা ছবি আমার একদম ভালোলাগেনা,এখন সুদু ভালোবাসা আর ফাজলামিরর ছবি বানায়",0,entertainment
পাঁচ পর্ব করি আপলোড দেন,0,entertainment
মান্না মতো নায়ক আর পাওয়া যাবে না,0,entertainment
এই মুভি টা ফুল দেনভাই,0,entertainment
বেলাকুচ পাওয়া মুশকিল,0,entertainment
কমেন্ট দেখে নাটক দেখতে আর ইচ্ছা করলো না।,0,entertainment
শাকিব খান বাংলাদেশে হিরো,0,entertainment
"সাকিল খান ও পপি অভিনিত, অগ্নি সাক্ষী ছবিটা আপলোড দিবেন প্লিজ",0,entertainment
সমাজকে সবচেয়ে প্রশ্নবৃদ্ধ করেছে তথাকতিতো কিছু মিডিয়া যতো আজেবাজে বিশয় জনসম্মুখে উপস্থাপনা করা এদেরকাজ কি দরকার ছিল পতিতা নায়ীকা সানাইর ব্রেস্ট নিয়ে টানাহিছরা করা আমি এই মিডায়র তীব্র নিন্দা জানাই।,0,entertainment
ফারিয়াকে ঘাড় ধাক্কা দিয়ে বের করে দেওয়া উচিত ছিল ওর কি দহ্মতা আছে মাসুদ রানা নির্বাচিত করার এর মধ্যে আবার সারাহ্মন মোবাইল টিপা টিপি,0,entertainment
গানটা শেয়ার করার জন্য ধন্যবাদ,0,entertainment
"আমার কষ্ট হলে এই গান টা শুনি সব সময়,",0,entertainment
সবকিছু ঠিক হয়েছে তবে পুরোটা বরিশালের ভাষা দিয়ে করলে আরো বেশি সুন্দর হত।,0,entertainment
দর্শক শুধু নন মিডিয়ায় আরও অনেকেই এরকম জীবনযাপন করার কারনে বিভিন্ন সময় সমালোচিত হয়েছেন! মিডিয়া থেকে কিভাবে এই সমস্যা দূর করা যাবে বলে আপনার মনে হয় জানান নিচের কমেন্ট সেকশনে!,0,entertainment
আমন গান কখন সুনি নি,0,entertainment
নাসরিন কে নায়িকা হিসেবে দেখতে চাই।,0,entertainment
চনচল মনেই নাম্বার ১,0,entertainment
এ মুভি অন্য চ্যানেলে আছে বেষ্ট রুবেল,0,entertainment
ফাহমি ভাইকে দেখে মনে হচ্ছিল পুরাতন কোন নাটকে তার স্বভাব সূলভ অভিনয় করছে😂😂😂,0,entertainment
মাগো তোমার জন্য নাটক চাই,0,entertainment
আমিন খান সুপাস্টার নায়ক।,0,entertainment
এই ছবির প্রায় অভিনেতা মৃত্যু বরন করচে!,0,entertainment
যতবার শুনি ততই ভালো লাগছে,0,entertainment
"আমার একজন মেয়ে বন্ধু দরকারকেউ হতে চাইরে মেসেস করেন, ও মেসেসে ইমো নাম্বার দিবো",0,entertainment
কি বেপার ভাই আর কোন ছবি পাইতেছি না কেন ভাই যদি পারেন তাহলে আজকে একটা ছবি দেবেন ভাই,0,entertainment
গাঁজাখুরি নাটক,0,entertainment
তোদের বাড়ি বরিশাল<br />রোহিঙ্গা দের পরে তোদের সম্মান,0,entertainment
চ্যানেল আইয়ের বিরুদ্ধে প্রতারনা মামলা করা দরকার ছেলেরা ওখানে মাসুদ রানা হতে এসেছে মা সুদ রানা নয়,0,entertainment
আগের চর্বিওয়ালি দের থেকে মাচ বেটার আইটেম সং গার্ল 🙊👍ভালো নাচে 👌👎👎গানের কথা গুলা খুব ই নিম্ন মানের বাংলাদেশি সং এ গানের কথার দিকে নজর দেয়ার সময় হয়েছে কারন ভিডিও দেখতে ভালো হলে ও কেউ যদি গানটা জাষ্ট শুনে হেডফোন দিয়ে আমি নিশ্চিত তার ভালো লাগবেনা ।কিপ ঈট আপ ✌,0,entertainment
এমন নাটক সমাজের উপকার হবে,0,entertainment
"কক্সবাজার বার্মিজ মার্কেটে আমরা বন্ধুরা মিলে টিক নিলয় ভাইয়ের মত করেছি, বার্মার মেয়েদের সাথে অনেক মজা করেছি যত দিন তাকছি ততদিন গিয়েছি তবে বাংগালির মেয়ে ছিল না তবে তাদের সাথে অনেক মজা করেছি, কারো সাথে এই রকম হয়ে তাকলে রিপলে দিবেন।",0,entertainment
আগা মাথা নাই মুভির ফালতু,0,entertainment
আমার প্রিয় নায়ক জসীম,0,entertainment
ছবির রেপ গুলা বালো লাগলোনা,0,entertainment
জুতা আর মোজা দুইটা দিয়া একসাথে সবার গালে পিটানো উচিত ফালতুর বাচ্চাগুলা।তাহসিন ভাইয়া তুমি কই। একটা আনলিমিটেড ভরে দিয়ে যাও তো,0,entertainment
আশা করি অনেক সুন্দর হবে,0,entertainment
সফল কমার্শিয়াল ছবি। শাবনূর সফল অভিনেত্রী।,0,entertainment
কি যে বলব ভাষাই হারিয়ে গেছে,0,entertainment
এইতো দেখি ডিজিটাল প্রেম,0,entertainment
ভাই ওক দিয়ে সরকার বালতুলবি,0,entertainment
মাগী😀😀😀,0,entertainment
শাকিব খান একজন ঠক বাটপার,0,entertainment
মনের মানুষ মুভির মতো রবীন্দ্র-নজরুল নিয়ে মুভি চাই।,0,entertainment
আর ইভানা আপুর ওয়েট কমানো উচিত..... যেইভাবে মোটা হচ্ছে😣,0,entertainment
শাবানা ম্যাডামের ছবিগুলো যেন একটা জীবন্ত জীবন।।আমি ছোট বেলায় অনেক দেখীছি কত যে কেদেছি... এখনো আমি অফিসে কাজ না থাকলে বসে বসে এসব দেখী ছোখে পানি চলে আসে।। খুব সুন্দর ছবিটা।,0,entertainment
মনের মত যতবার দেখি কি বলব,0,entertainment
"আপনাদের আপলোড দিওয়া সব মুভির গান আপলোড দিয়েন ফোল HD এন্ড ফোল ইস্কিন করেbro, piz piz piz bro,,,,",0,entertainment
মাগি তোদের জন্যই আজ যতো সমস্যা।,0,entertainment
"কবে দেখেছিলাম মনে নেই। তবে ০৮ মার্চ ২০১৯ এ দেখলাম আর প্রায় ৩০০ মত কমেন্ট পরলাম, সেই ছোট বেলার কথা মনেপরে গেল। কতটা পরিবর্তন হয়েছে সবকিছু??সবাই ভাল থাকবেন মা,বাবা,ভাই-বোন ও পরিবারের সকলকে নিয়ে।ধন্যবাদ",0,entertainment
তুই তো অশান্তি সৃষ্টি করে দিলি।তুই তো পর্ণ স্টার,0,entertainment
আমি প্রতিদিন সাকিব খান এর সিনেমা না দেখলে আমার ঘুম আসে না।কিন্তু আমার রিয়াল হেরো হলো সাকিব খান,0,entertainment
ভাই রিকুয়েষ্ট একটু তাড়াতাড়ি দিয়েন ৮৪ এপিসোড টা 🙏🙏,0,entertainment
গানটার পিছনে % অবদান ভারতের।,0,entertainment
"প্রথম বার যখন ছবিটা দেখছিলাম তখন আমাদের বাসায় কারেন্ট ছিলো না।।ব্যাটারি দিয়ে দেখছিলাম।আবেগময়, শিক্ষাময় একটি অসাধারণ ছবি।",0,entertainment
শেষের গল্পটা অসাধারণ ছিল,0,entertainment
রুবেলের আরো ছবি চাই,0,entertainment
আমি একটা সপ্ন তুৃমি একটা আশা এরিনাম বলবো তোমার আমার ভালোবাসা,0,entertainment
চালিয়ে যান ভাই সাথে অাছি,0,entertainment
নাটক টা অনেক অনেকহিট হতোও ফারহান ভাই হলে,0,entertainment
শিহরিত,0,entertainment
আমি বাংলা মাতরাম এর বাদেও বুজেনা অখন কিতা খরতাম?,0,entertainment
অনতরজালা,0,entertainment
আমারও প্রিয়,0,entertainment
"আমার কাছে গান টি অনেক ভালো লাগে,,,",0,entertainment
সব বিচারক খুব বেয়াদব।,0,entertainment
ভাল লাগে বাস্তব,0,entertainment
ছবিটা একের মাগার শব্দটা ডিস্টার্ব,0,entertainment
তোর মুখে আল্লাহর নাম নেওয়া মানায় না।,0,entertainment
"ভালো লেগেছে তো আবার খারাপ লেগেছে একজনের সাথে প্র‍েম করে আরেক কথা সারা দেয়া কি ঠিক মেয়েরা কি এমনি কস্টা হয়া,,,হারে জীবন",0,entertainment
এইটা মভি না নাটক ইডিটিং এত খারাপ,0,entertainment
এইতো আমাদের বাংলার গল্প,0,entertainment
সানাই হতে চাই এমপি আর সানাই এমপি হলে ভাল হবে দেশের দুধের চাহিদা পুরোন হবে আর সানাই তুই হিরো আলম কে বিয়ে করতে চাইলে ও হিরো আলম বিয়ে করবে না,0,entertainment
কেও কি যানো যে বাংলা ব্যাকারণ ভিডিও টা কবে আপলোড হবে।,0,entertainment
জাতির প্রশ্ন : আমিন খান কি সারা বছর সাইড হিরো হিসেবে কাজ করবে ??,0,entertainment
অনন্য আপনার ছবি গুলি অনেক সুন্দর হয়ছে,0,entertainment
ভালোবাসার নামে এতো অভিনয়ের কি দরকার ছিল। পাষানি,0,entertainment
নাটকের বাল হইছে,0,entertainment
"এই এক মুভির কত গুলি চেনা মুখ চলে গেছে,,হুমায়ন ফরিদী, ব্যাক আনোয়ার,দিলদার,আনিছুল রহমান।",0,entertainment
অসাধারণ হয়েছে ভাইয়া,0,entertainment
মান্না ভাইয়ের মতন নায়ক বাংলাদেশের আর কখনো আসবে না,0,entertainment
সব কয়টা বিচারক কে জুতা দিয়ে পেটানো উচিৎ। ফালতু সব।,0,entertainment
আরো ভালোবাসবো তোমায়,0,entertainment
আমার জীবনের সব চাইতে বেষ্ট মুভী এটা,0,entertainment
"মিমের চেহারা একদম বাচ্চা বাচ্চা ,বড়ই মায়া মায়া ।",0,entertainment
"জনাব, youtube&#39;a ভিডিও দিতে না পারলে তো ভিডিও এড এখানে চোদাবেননা ।",0,entertainment
আহ গ্রারামের দিশ্য কি দারুন,0,entertainment
তুই বড়ই পালতো বেটি।এই বেটি জাতিকে দুধ উপহার দেয়।এরে হারাম জাদি তুই জাতিরে নিছতলা উপহার দেছ।,0,entertainment
😅😅 তোরা এত্ত যাউরা ক্যারে ভাই 😂😂,0,entertainment
"ছোট বেলায় ছবিটা দেখেছিলাম অন্যের বাড়িতে ,, ঘরের মধ্যে মাটিতে বসতে ও দেইনি , দরজার সামনে দাঁড়িয়ে দেখছি। তারপর কত যে ভালো লাগত। সোনালী দিন গুলো কোথায় হারিয়ে গেল।",0,entertainment
লক্ষ টাকার দুধ বেশি করে চা খান মজা হবে 🍼🥛🥛☕️,0,entertainment
কাট পিচ মুভি ফুল এইডি চাই ছবির নাম এসপট ডেট চাই ভাইসাব,0,entertainment
অন্তর আগুনে অন্তর পুড়ে যায়।,0,entertainment
"প্রতিদিন ৪ টা শো হতো হলে কিন্তু এ ছবির জন্য তখন একটা শো বেশি করতে হয়েছিলো, সকাল ৯ টার শো, গোবিন্দগঞ্জ তিথী সিনেমা হলে",0,entertainment
মোশাররফ করিম মানেই নতুন কিছু,0,entertainment
জান্নাতের খবর কি?আজ আপলোড দিবেন না।,0,entertainment
"তোমার অভিনয় দেকলে আমার মন ভরে জাই,,বস্",0,entertainment
"এদের বিয়ে মানে পুতুল খেলা,,,,,,বেলা শেষ খেলা শেষ,,,,???",0,entertainment
ভালো রোমানটিক কিছু দেখাও,0,entertainment
নতুন দের সুযোগ করে দেওয়া উচিৎ,0,entertainment
আমিন খানের মুভি ভাল হয়,0,entertainment
"মান্না ভাই যখনি তার মুভি,দেখি তখনি দুচোখে কান্নার পানি চলে আসে,দোয়া করি আল্লাহ যেন আপনাকে জান্নাতুল ফেরদৌসের নসিব করে,আমিন।",0,entertainment
দারুন লাগছে ছবি টা,0,entertainment
বাবা হবার আগেই মুভিটা দেখে কান্নায় ভেঙ্গে পড়লাম।জানিনা যদি সত্যি সত্যিই এমন একটা সময় আমার জিবনে আসে তাহলে আমি কি করবো...?মুভিটা দেখে নিঃশ্বাস নিতে ও কষ্ট হচ্ছিল। মান্নার রুহের মাগফিরাত কামনা করি এবং পরিচালক সহ সকল অভিনেতাদের কৃতজ্ঞতা জানাই এমন সুন্দর মুভি উপহার দেবার জন্য।,0,entertainment
সানাইয়ের জন্য হিরু আলম,0,entertainment
অনেক ভাল হইসে ফিল্ম টি.. হাসবেন্ডের ক্যারেক্টার টা যিনি এক্টিং করসেন মাশা আল্লাহ👌,0,entertainment
পতিতার প্রেম || Potita || bangla upcoming movie 2018 ||,0,entertainment
মিউজিক চুরি।বাহ ভালোই।,0,entertainment
"অনেক কস্ট হয়, যে আমার প্রিয় নায়ক মান্না বেচে নেই, মান্না ভাইয়ের সব ধরনের Acting ভিন্ন ধরনেরআমার কাছে খুবই ভালো লাগে, তার আসার মডেলআরও ভালো লাগেঅসাধারণ সব ছবি, ছবির প্রিনটা অনেক ভাল ।",0,entertainment
সাকিব অপু সেরা জুটি,0,entertainment
এমন একটা সময় আমারও ছিলো,0,entertainment
ছাগল দিয়ে হালচাজ হয় না ঠিক তেমনে মারুফ কে দিয়ে সব ছবির অবিনয় হয় না,0,entertainment
শাকিব অপু দারুন জুটি। বইটি খুব ভালো লাগল আমাদের ইউনিটের সকলের। তোমাদের আরো বই দেখতে চাই।👌👌👌💐💐👌👌👌👌👌,0,entertainment
বরিশাল মানে মোশারফ,0,entertainment
এই নাটকের লিংক পাওয়া যাবে কেউ কি জানেন???<br /><br />অনেকদিন যাবত অপেক্ষায় আছি নাটকটার জন্য 😥😥😥😥,0,entertainment
খুব ভালো লাগলো ধন্যবাদ,0,entertainment
অঞ্জনা বাংলাদেশের ডেয়ারিং ডেঞ্জারাস সুন্দরী নায়িকা।,0,entertainment
প্লিজ সানাই কে প্রবাসে পাঠিয়ে দেওয়া হোক এখানে দুধের অনেক অভাব,0,entertainment
দেশে আগে ছিলো মিরজাফর এখন আছে চোর আর আগে পরে দুটোই মিলিয়ে আমাদের দেশ টা এই অব্যবস্থা,0,entertainment
খুব একটা ভালো ছবি,0,entertainment
"ন্দনভনক ই,ক",0,entertainment
নাটক টা অনেক সুন্দর।।।।।তাহসান ভাইয়ের অভিনয়টা অনেক ভাল লাগছে,0,entertainment
"আমি এই ছবিটা কতবার দেখছি সেটা মনে নাই,যত দেখি মন আরো দেখতে চায়, আর প্রতিবারই চোঁখে পানি চলে আসে।",0,entertainment
"এদের মধ্যেও ভালো মানুষ আছে, আমি এদের মধ্যে থেকে আমি একজন নিবে অাতি আপন করে নিতে চাই।থাকলে।প্লিজ আমার সাথে যোগাযোগ করবেন 01820137864",0,entertainment
ধন্যবাদ বস,0,entertainment
ওস্তাদের মাইর শেষরাতে,0,entertainment
ইনেক সুন্দর হইছে,0,entertainment
নাটক খুব ভালো হয়েছেকিন্তুু শেষ মিলন টা ভালো লাগে নাই,0,entertainment
নামধারী পতিতাকে বাংলাদেশ থেকে ভারতে রপ্তানী হল শুঁটকির গন্ধ অনেক।,0,entertainment
গানটা অনেক সুন্দর হয়েছে,0,entertainment
ভুলে ভুলে জীবনটা শেষ ভালোবেসে কি ভুল আমি করেছি যতটা না কাঁদে মানুষ,0,entertainment
পরিবারের সদস্যদের একটি কীটপতঙ্গ কারণেআজ সোনই পুরির এই পরিনতি,0,entertainment
খুব ভালো মভি,0,entertainment
ওই দিনে আর আসেবনা সাবনুর আর রিয়াজ,0,entertainment
আগের ছবি গুলো খুব খারাপ!😓😰🇧🇩,0,entertainment
ভাই টাইটেল টা সুন্দর হয় নাই,0,entertainment
সাকিব ভাই আপনার আগের ছবি দেখার মতো এখন কি ছবি করেন,0,entertainment
এত দেরি হয় কেনো,0,entertainment
মিয়া খলিফা আর সানি লিওনি ও ভার্জিন,0,entertainment
"এই নাটকের কথা বন্দ কেন,,,।",0,entertainment
রিয়াজ ভাইয়ের এ সমস্ত ছবি হাজার বছর তাকে বাঁচিয়ে রাখবে। আসলে রিয়াজ ভাইয়ের সাথে ষড়যন্ত্র হয়েছে।,0,entertainment
"পুরানা ছবি দেয়ার জন্য ধন্যবাদ । ভাই “ অংশীদার , বিনি সুতার মালা, সুলতানা ডাকু, ও বঁাধনহারা “ ছবিপুলো upload দিন ।",0,entertainment
নাদেখেইকমেন্টেরকরলামকারণকমেন্টেরসবাইভালবললতাই,0,entertainment
ভালবাসা তরী ব্যান্ডের পক্ষ থেকে।বাংলা ঢোলের সাথে আমাদের ফোক গান শুনার আমন্ত্রন রইলো।,0,entertainment
ছিঃ ছিঃ ছিঃ জয় ভাই শেষ পর্যন্ত আপনিও এর ইন্টারভিউ নিতে পারলেন আপনারাকি আর ভালো লোক খুজে পেলেননা,0,entertainment
অডিও পাব কোথায়,0,entertainment
খুবই ভালো লাগল,0,entertainment
বলে লাভ নাই এদের কিছুই হবে না,0,entertainment
ভাই দিনমজুর ছবিটা দিবেন,0,entertainment
কাল সময় টিভিতে নিউজ দেখলাম এই শো না বুয়া এই শো য়ের সিলেক্টেড ছেলেদের কে নিয়ে মুভি বনানো হবে না।,0,entertainment
নিলয় অহনার নতুন নাটক চাই,0,entertainment
আখম হাসান সেরা,0,entertainment
ইমু তে রোমান্টিক মজার কেউ কি আছো।,0,entertainment
প্রশ্নগুলো মারাত্তক ছিল।,0,entertainment
"স্যার নাটক টা আমি আরো অনেক আগে দেখেছিলাম,, আবার ও দেখতাছি ।।",0,entertainment
সালমান শাহের সুন্দর মুভি খুব ভাল লাগলো,0,entertainment
"আমার মতো গরীব ইউটিউবারদের একটু দয়া করুন ভাই, বোন, দাদা ও দিদিরা। ভিডিও গুলো আপনাদের ভালো লাগবে, কথা দিচ্ছি। এই গরীব ছেলের চ্যানেলটি বেড়ে উঠতে এবং স্বপ্ন পূরণে সাহায্য করুন প্লিজ, এটাই আমার ইউটিউব চ্যানেল।",0,entertainment
"প্রিয় সালমান প্রিয় হোমায়ুন ফরিদী আমাদের মাঝে আর আসবেনা,, সুবর্ণা মুস্তাফা হুমায়ুন ফরিদী কে ছেড়ে তার নিজের স্বার্থ হাসিল করেছে আর সামিরা চৌধুরী সালমান শাহকে হত্যা করে সুখের সংসার করছে কী আজব দুনিয়া রে ভাই",0,entertainment
নাটক টি কার কার বাল লাগচে,0,entertainment
আমিগর্বিত কারণ আমি অমর নায়ক সালমান শাহ এর একজন ভক্ত হতে পেরে।<br />0096895217863,0,entertainment
দারুণ সুন্দর হইছেআর ফুল নাটক টি দেখেছেন কে কে।,0,entertainment
বাংলাদেশের নাটক গুলো ভালো কিন্তু নাটক করতে ইসলাম বিদ্ধেশী কোন প্রকার কর্মকান্ড না হয়।,0,entertainment
আন্নেরা দেক্সেন্নি হোগাখাইল্লরা কি নিয়া কাহিনী করচে ক্যান,0,entertainment
চােখের পানি ধরে রাখতে পারলামনা,0,entertainment
রাজনীতি এবং একশ্যান ছবির সুপার অ্যাকটর হিরু এক মাএ আমিন খানি আছে বর্তমানে আর কেউ নেই।। তাই পরিচালক স্যার দের কে বলছি আপনারা কি আজে বাজে নায়ক দিয়ে ছবি বানান কেন। আমিন খান খুব খুব ভাল নায়ক।,0,entertainment
পরিচালক গুলা য়ে কি বুজতে পারিনা আমিন খানরে পালাই রাখছে ৬ নাম্বারেয়দি দেখি তবে আমিন খানের জন্য,0,entertainment
অসাধারণ এরকম সিনেমা খুব কম তৈরী হয়েছে !<br />সব অভিনয় অভিনেত্রীর অভিনয় অতুলনীয় !<br />আমি ভারত থেকে বলছি !,0,entertainment
ছবিটা দেয়ার জন্য ধন্যবাদ,0,entertainment
ইন্টারনেট থাকার কারণে 25 বৎসর পর আবারও দেখতে পেলাম,0,entertainment
দেশে কি নায়ক অভাব পরেছে,0,entertainment
এখানে যারা আছে আমার মনে হয় ঘুষ দিয়ে এসেছে।,0,entertainment
হা হা হা জোস,0,entertainment
এরা সব কে অনুসরণ করতে ছিল! 🤣🤣,0,entertainment
"ভাই ছবিটি অনেক সুন্দর তাই বলছি যদি পারেন তাহলে ইলিয়াস কানছনের,,, অন্ধ বধু,, শান্তির বদলে শান্তি,, মাটির কসম,, লটারি,, দিনমজুর,, টপ মাস্তান,, এই ছবি গুলো যে কোন একটা ছবি দিন ভাই আপনার কাছে অনুরোধ",0,entertainment
"ভাষা বলার নাই, অসাধারণ অভিনয়",0,entertainment
ছবি এই ছবিতে লাইক দিয়ে শেয়ার করবেন,0,entertainment
বালের বিচনাকান্দি,0,entertainment
সেই হয়েছে,0,entertainment
একটু তারা তারি দিবেন ৮৯ প্লিজ,0,entertainment
কার কার কাছে সাকিব ও অপুর সিনেমাভালো লাগে লাইক ও কমেন্ট করুন প্লিজ,0,entertainment
আমি আসিফ খান আমার ছবি সবাই হলে গিয়ে দেখবেন আমার ছবির নাম প্রেম নামে ছলনা,0,entertainment
এ ছবির নায়ক কে মাথায় ঢুকলো না🤣🤬,0,entertainment
বিচারকেরা নিজেরাই তো অভিনয় পারে না।,0,entertainment
তুই আর ভিডিও দিসনা।,0,entertainment
আমিন খান ভাইয়া সুপার হিরো,0,entertainment
বড় দারিআলা টারে গুইনা গুইনা জুতার বারি মারা উচিত,0,entertainment
এটাই উচিত শিখা,0,entertainment
ভারতী বাংলা মুভি কে আর কত কপি করে চলবেন এবার নিজেরা নিজের পায়ে হাঁটতে একটু চেষ্টা করেন বাংলার পরিচালক ভাইয়েরা,0,entertainment
এই ছবিটা ভালো লাগলো কারণ সাকিবকে পুলিশ ধরেনি,0,entertainment
অসাধারণ একটা গান আপনারা বোঝেন না সেই জন্য বাজে কমেন্ট করেন,0,entertainment
দেশে কি নায়ক নায়িকার অভাব পড়ছে,0,entertainment
"নতুন হোরর ফিল্ম (ভয়ানক সফর)<br />ট্রেইলার<br /><a href=""https://www.youtube.com/watch?v=yOArpNRSHZ4"">https://www.youtube.com/watch?v=yOArpNRSHZ4</a><br />দেখার আমন্ত্রণ লইলো",0,entertainment
আমাদের সময়ের ছবি।এহতেশামের ছবি মানেই ভালো কিছু,0,entertainment
"আমার এই গরুর গাড়ি ছোটে সবার বাড়ি ইঞ্জিনের আগে ছুটে যায় আমার গাড়ির জুরি নাই, বৌ যাবে স্বামীর ঘরে সংসার সাজাতে দুই চোখে পানি ঝরে মা বাপ ছাড়িতে কত কিছু দেখি আমি গায়ের পথে,,,।",0,entertainment
মোশারফ আছে বলেই বাংলা নাটক আজ এত জনপ্রিয়,0,entertainment
কিছু অন্য প্লানেট থেকে আসা এলিয়েন আনলাইক দিছে।ওদেরকে দুনিয়া ত্যাগ করে ওদের চ্যাংচু গ্রহে ফেরত জানাতে জাতিসংঘের প্রতি আহবান করছি।,0,entertainment
"এগুলোকেই বলে নষ্টা মেয়ে, পছন্দ যখন নাই করবি, বিয়ে করলি কেন",0,entertainment
ইসলাম নিয়ে বেয়াদবি করা চলবেনা &#39;।,0,entertainment
রিয়াজ ভাই আর শাবনূর আমার বেস্ট জুটি,0,entertainment
দয়া করে ৮৫ পর্ব থেকে চালু করেন,0,entertainment
"বর্তমানে রিয়েলীটি এমন হয়, পরিচালকরা আগে এমন করে, তারপর নায়িকী খ্যাতি পাই,, মিডিয়াতে এইটা পতিনিয়ত চলতেছে,, চলতেই তাকবে মিডিয়া জগতে কোন কেউ ভালো না,,সবাই খারাপ...",0,entertainment
আসলে ওপু সরিল খুবি পছন্দ সবার চখে তাই না,0,entertainment
বিষ দাত মুভিটা চাই।,0,entertainment
ঘি বেন টেক করে পেল নইলে সুপার ইস্টার নায়েকা হতে পারবনা <br />তরা শালারা কপি করার লাই গা বেডা মানুষ পারলে নিজের গিয়ানে কিছু কর,0,entertainment
জয় ভাই আপনি আমার পছন্দের একজন মানুষ। তবে গেস্ট হিসেবে এমন অরুচিকর মানুষকে ইনভাইট করাতে আপনার রুচি উপর আমার প্রশ্ন জেগেছে। সানাইর না আছে চেহারা না আছে পারসোনালিটি। সোজা কথা,0,entertainment
বাঙালি জীবনেও আগাইতে পারবে না। এই ধরনের শো বাইরে অনেক হয়।কোন সমালোচনা হয় না বাঙালি চুটকে ইউটিউবাররা সামান্য ভিই পাবার জন্য কী শুরু করেছে।,0,entertainment
ভাইরাল হওয়ার জন্য দুনিয়ায় এসব করছেন আপনি কি চিরজীবী আপনার কি মৃত্যু হবে না আপনি যদি মরন কে ভয় করেন তবে এখনো সময় আছে ভালো হয়ে যান। আল্লাহ মাফ করুক।।।,0,entertainment
"বোবা করে দাও আমাকে বিধি! যার কাছে বলি কথা সেই দেয় মনে ব্যাথা বিশ্বাষ করবো কাকে, আমি বিশ্বাষ করব কাকে।",0,entertainment
আমার ও রিয়াজ কে ভালো লাগে,0,entertainment
"কমেন্ট টা রেখে গেলাম 😑<br /><br />এটা আমার প্রজন্মের মুভি, এই কথাটা ৫০ বছর পর বেছে থাকলে সেই প্রজন্মকে বুক ফুলিয়ে বলতে পারমু😍",0,entertainment
"সত্যিই ছবিটা খুব সুন্দর,",0,entertainment
এই সময়ের বয়সটা এরক হয়,0,entertainment
ভালোই হলো। ওর পরিবারে আর দুধের সংকট থাকবে না।,0,entertainment
বালের জাজমেন্ট ওদের থেকে আমিও ভালো পারবো । নিজেগো নাই যোগ্যতা জাজমেন্ট করার আবার তারা আসছে জাজমেন্ট করার।,0,entertainment
দুরতরি পুরাই ফালতু নাটক,0,entertainment
"নাটকটা অনেক ভালো লাগলো,,,",0,entertainment
কই তুই,0,entertainment
রিয়াজ এর অসাধারন মুভি,0,entertainment
খুব সুন্দর লাগছে very nice,0,entertainment
শেষ কথা গুলি অতি বাস্তব?,0,entertainment
ক্যামেরা ম্যান সালা তুই নতুন নাকি এত নড়াচড়া করাস কেন,0,entertainment
এই টা কোন নাটকের জাতের মধ্যেই পরে না!!,0,entertainment
ইস এত দিন কোথায় ছিল্,0,entertainment
"গোপন সমস্যার জন্য আজই কল করুন I প্যারিস হারবাল I parish h a r b a l Final <a href=""https://www.youtube.com/watch?v=7wADK6xTrN8"">https://www.youtube.com/watch?v=7wADK6xTrN8</a>",0,entertainment
ভাই আরো মুভি দেও খুব সুন্দর,0,entertainment
খুব ভালো লাগলো মুভিটা,0,entertainment
"মেয়েদের চ্যানেল তো,এমনেই ভেজাল থাকবেই,,,,উল্টা পাল্টা নাটক ছারে",0,entertainment
এদের তো জনসম্মুখে জুতা পেটা করা উচিত,0,entertainment
ভাই জজ দেরকে জুতা মারা দরকার ছিল ভাই আপনি জজ দের কে কিছু বলতেছেন না কেনো,0,entertainment
আগের মতো ভাল লাগে না,0,entertainment
লাইক পাওয়ার যোগ্য 😍,0,entertainment
"আচোদা মার্কা মুভি,,এ জন্যই বাংলা মুভি দেখতে মন চায় না।হাসপাতালে অসুস্থ লোক কি করে গানে থাকে??",0,entertainment
বরাবরই বাঁশ ঢুকাই দিলেন ভাই,0,entertainment
"প্লীজ লেখা গুলো সুন্দর করে লিখুন, আমরা যারা কমেন্ট পড়তে আসি, তাদের জন্য পড়া কষ্ট হয়ে যায়।",0,entertainment
সালমান শাহ অনেক জনপ্রিয়,0,entertainment
দুই নায়েক সুপার,0,entertainment
দাড়িওয়ালা এই মফিজ টা বিচারক না এটা একটা জঘন্য একজন বিচারকের আচরণ কেমন হওয়া উচিত না আরে আগে আপনাকে কয়জনে ভালো করে চিনে সেটা চিন্তা করে দেখেন চেয়ারে বসে তো বড় বড় কথা বলতেছেন কেউ লাইফের শুরু থেকে মাসুদ রানা হয়ে আসে না আর আপনিও বিচারক হয়ে আসেন নাই,0,entertainment
আরো গান আপলোড দেন ফোল HD এন্ড ফোল ইস্কিন,0,entertainment
এর জন্যই অামরা বাংঙ্গালি অামরা কেও ই গান শুনি না দেখি গানের ভিডিও অারে ভাই অাপনারা অাগে প্রিতম ভাইয়ার গানের কথা গুলা শুনে কিছু শিখুন পরে কমেন্ট করেন ভাইয়া গানের কথা গুলা যেমন সত্য তেমন ই মঝার অাপনি বলেই হয়ছে তা না হলে হতো না এমন ভালো গান,0,entertainment
এবং এই নাটক টা লাইক দিলাম শুদু তানজিন তিশার কারনে,0,entertainment
আমার ভালোবাসা মানুষ আমার সাথে একরকমকরবে তা জানে,0,entertainment
মাইর দেওয়া উচিত,0,entertainment
আসলে অনেক ভাল নাটক,0,entertainment
এতো সুন্দর গানটিতে কিছু কুলাঙ্গার ডিজলাইক করেছে।,0,entertainment
আসলেই কিন্তু বাস্তব,0,entertainment
লজ্জা না থাকলে যা হয় আর কি,0,entertainment
তোদের ভালবাসা হাহাহাহা,0,entertainment
নাটকটা দেখে অনেক ভালো লাগলো0545052645,0,entertainment
প্রতিটি জিবন একটি সম্পর্কের কাছে দূর্বল থাকে ।যেখানে কিছু অবুঝ সরলতা আর কিছু বর্ণিল মুখের ভাষা জিবন কে স্বার্থহীন ভাবে কাঁদায়.।যা কেউ দেখে না.,0,entertainment
পতিতা পলি সরদারা ওনেক খারাপ জাবার চাইলে মারে মেয়ের মারে কারা নিয়ে জাইওদের দরেন,0,entertainment
বাংলাদেশে একজন নায়ক ছিল যিনি মহানায়ক সালমান শাহ’র জায়গা দখল করে নিতে পারতেন । সালমান শাহ’র মত যার অসাধারন চেহারা ছিল তিনি হলেন সাকিল খান।কিন্তু তিনি তার ভুলের জন্য জনপ্রিয় হতে পারলেন না। অজড়ে ঝড়ে পরে গেলেন।,0,entertainment
আচ্ছা বাংলাদেশে কি মিসা চাড়া আর কোন বিলিন নাই,0,entertainment
"মোশারপ এর বউ এর জন্য, নাটক দেখতে ভালো লাগে না।",0,entertainment
সত্যি ভিডিওটা দেখে কিছু না বলে যেতে পারতেছিনা সত্যি ভাই অসাধারণ হয়েছে আর আপনি যাদের নিয়ে কথা বলছেন তারা নিজেরা যদি ভদ্র হত তাহলে ভদ্রভাবে কাউকে ব্যবহার করত না যতসব আবাল বাংলাদেশের পাগল আর কি ভুল করছে তাদেরকে ওই জায়গাতে না দিয়ে রাস্তায় দিলে ভালো হতো,0,entertainment
অতিত বর্তমান কে বিশায়িত করে😞😞😞😞😞😞,0,entertainment
নাটকের শেষ খুব বাজে।,0,entertainment
আলেকজান্ডার বো সুপার হিট,0,entertainment
"তাহসান মানে ভালোবাসার আরেক নাম,,,,,,,,,,,,,,,,",0,entertainment
দিন যাবে দিন আসবে কিন্তু মান্নার মতে এমন নায়েক আর আসবে ও না আর কিনে দিন হবেও না অনেক নায়ক কে অনেকেই পছন্দ করে না কিন্তু মান্না ভাই কে আর সালমান শাহ্ ভাই কে সবই পছন্দ করে এবং সবাই তাদের দুই জন কে ভালোবাসে আর তাদের জন্য সবাই দোয়া করে এই আল্লাহ তাদের কে জান্নাত ধান করে আমিন,0,entertainment
"অসাধারণ একটি গল্প ধন্যবাদ প্রিয় সবুজ সারোয়ার ভাই ভালো গল্প উপহার দেওয়ার জন্য <br />সে সাথে ভালো অভিনয় করার জন। ধন্যবাদ চৈতি ইসলাম এবং পার্থিব মামুন, রাজন, রিগান,আলমগীর সবাই ভালো অভিনয় করেছেন।",0,entertainment
এটা কোন জায়গায়<br />কেউ বলো,0,entertainment
"কমেন্ট পরে দেখা শুরু করলাম,আসা করি ভাল হবে",0,entertainment
ইন্ডিয়ার মতো হওয়া আনেক দেরি ।,0,entertainment
এক কথায় বলা যায় অসাধারন মুভি,0,entertainment
আমি জানি না নাটক দেখি শেষ করে,0,entertainment
বাংলা নাটক অনেক ভালো ইন্ডিয়ান নাটক দেখে পাগলে,0,entertainment
দিপু অনেক সুন্দর একটা চরিত্র ফুটিয়ে তুলেছে।<br />সে ২০১৯ এ আমার থেকে ও বড় বয়সে। কিন্তু ছোট বেলায় যে সে কিউটের ডিব্ব ছিল সে ব্যপারে কোন সন্ধেহ নাই☺,0,entertainment
আমি হলে বস সাকিব আল হাসানের মত নিজের বাড়াটা দেখায়ে দিতাম,0,entertainment
সালারা সব পর্ব দিলে কি হয়,0,entertainment
মুভির মানে যারা বুঝলো না তারাই কেবল ডিসলাইক দিল,0,entertainment
পতিতা মেয়েদের কথা শুনে আমি অনেক কষ্ট পাইলাম,0,entertainment
তাকে নিয়ে আমি বাবি,0,entertainment
"ভাই সাকিবের,না কাব ছবিটা দেন",0,entertainment
"গানের সুর সুন্দর লাগছে অনেক অনেক ভালো, জার চাল নাই চুলা নাই তার সাথে প্রেম করাটা মোটেও ঠিক না হবাব কিহবাবে সাংসার কষ্ট লাগে কিন্তু শান্তি লাগে না পেটে ভাত না থাকলে প্রেম পালায়া জায় ভালো মানুষেঅপরাধ এটা",0,entertainment
মনে হয় জনি সিন্স এর নতুন পায়ছে। 😁😁😁,0,entertainment
খুব সুন্দর হয়েছে,0,entertainment
মেীসুমী এদেশের সেরা নায়িকা। তাকে জাতীয় চলচিএ পুরুস্কার কমপক্ষে ১০ বার দেওয়া উচিত ছিলো।,0,entertainment
অতি সুন্দর লাগলেভাই চালিয়ে জাও আমি কলকাতা থেকেই,0,entertainment
চবিটা দেখে চোখে পানি চলে আসলো,0,entertainment
"বালের পাটাকা, বালের গান",0,entertainment
ভাল লাগলো না।,0,entertainment
এই মেয়েরে নিয়া এতো মাতামাতি টিক হয়নি। আমি মাজার টিভির ফ্যান এই দেখে । ছি ছি আমাদের নারী সমাজ কি এর জন্য লড়েছিল। 😈😈😈😈😈😈😈😈😈😈😈😈,0,entertainment
মাসুদ রানা মানে কি বুঝলামনা,0,entertainment
"প্রসূন আজাদকে খুব দারুন লাগছেতো,,,",0,entertainment
আলগা ঢং আবার বলে সে ছোট কচি মানেটা বুঝাইতাছে শেনাবালিকা নাবুঝা বিয়া করছে নেকক্সট জেবিয়া করব ভাববো নাবুঝেই বিয়া করছে,0,entertainment
"আসল কাহিনী গুলোই ত কেটে দেওয়া হয়েছে, ছবিটা দেখে তেমন কোনো মজা পেলাম না, কারন একটাই কিছু অংশ কেটে দেওয়ার জন্য।",0,entertainment
অনেক সনদর নাটক আমার জীবনের সবথেকে সনদর নাটক,0,entertainment
"আসলে কথা সত্য, মিডিয়া ই পারে একটা জাতিকে নাংটা করে টেনে হিছরে মাটিতে নামাতে। এই নাটক দেখে নতুন প্রজন্ম কি শিখবে, শিখার কি আছে এতে?তবে এটা ঠিক নিজের সংসার ছেরে সেই আগের প্রেমিক বা প্রেমিকার কাছে পৌছানো।",0,entertainment
"রাতজাগা মানুষগুলো একটু অদ্ভুত হয়। সারারাত জেগে নিজের অতীতকে স্বরণ করে। কিছু মানুষ সেই অতীতের কারণে রাত কাটায় বেলকনিতে। আর কারো রাত কাটে চোখের জ্বলে বালিশ ভিজিয়ে! , এ মানুষগুলোর ভালবাসার রংধনুতে হয়ত সাতরঙের মিলন হয়নি। এদের ভালবাসার বাগানে হয়ত ফুল ফোটেনি। অবিশ্বাসের ঝড়ে হয়ত সেই রংধনু মিলিয়ে গেছে। অবিশ্বাসী কেউ একজন হয়ত সেই ভালবাসার বাগানে বিষ ঢেলে দিয়েছে। , এক সময় যে ছেলেটির হাতে থাকত প্রিয়তমার ছবি, তার হাতেই আজ শোভা পায় মদের বোতল! তার রাত কাটে মদের প্যাগে কিংবা বেনসনের সর্বনাশী ধোয়ায়। যে ধোয়ায় ছেলেটি তার স্বপ্নকে উড়িয়ে দেয়। ধোয়ার মতই বাতাসে মিলিয়ে যায় তার অনুভূতিগুলো! , সে মেয়েটি তার টানা টানা দুটি চোখে আজ আর কাউকে নিয়ে স্বপ্ন দেখে না। তার স্বপ্নকে গুম করে সেই চোখে আজ জায়গা করে নিয়েছে অশ্রুর সাগর। সেই সাগরে ডুব দিয়ে মেয়েটি আজো তার দুঃখ ভোলার ব্যার্থ চেষ্টা করে। তার রাত কাটে চোখের জ্বলে বালিশ ভিজিয়ে। , এরা দিনের বেলায় সবার সামনে নিজেকে স্বাভাবিক রাখে। দেখাতে চায় সে ভাল আছে, সুখে আছে। রাত এলেই তাদের আসল রুপ বেরিয়ে আসে। মুখ যতই বলুক ভাল আছি,মন ততই বলে আজো বেচে আছি,খুশিতে কেউ রাত জাগেনা।আনন্দে",0,entertainment
তোর মতো মেয়েকে পুরিয়ে মারা উচিত আল্লাহ তোর উপর গজব নাজিল করুক তোকে যে কি বলব ভাষা পাইতেছিনা।,0,entertainment
"চমৎকার,এভাবে যদি সচেতন হয়",0,entertainment
মোটামোটি ভালো লেগেছে।রাজু মালয়েশিয়া থেকে,0,entertainment
এই ধরনের আরও খোলা মেলা হট গান সহ ফুল মুভি চাই,0,entertainment
খুবি সুন্দ রমুভি সালমান শাহ চির ওমর আমার পিয় নাইক এর পর রিয়াজ মাননা আমিন খানশাকিব খান একটা নাইক হলবলদ,0,entertainment
তাহসান ভাই আপনি এ নষ্টা মিয়ের সাতে কেন নাটক করতে গেলেন,0,entertainment
হা হা শেষ দৃশ্যটা বেশি ভালো লেগেছে। 😃,0,entertainment
মিশার অভিনয় টা অনেক সুন্দর হয়েছে,0,entertainment
হাতানো যাবে নাকি কল্পনা কইরা হস্তমৈথন কইরা আগা মোটা গোড়া চিকন হইয়া গেছে মনে হয় ধজভঙ্গ হইছে,0,entertainment
আমিও শাকিব খান হতে চাই,0,entertainment
বইন তুই আজ গাজা একটু বেসি খাইছত,0,entertainment
এমবি কম। দিয়ে দেখতেছি। মোট কথা ভিডিও মিস করা যাবে না 😂,0,entertainment
খুুব সুনদর,0,entertainment
নিলয় ভাই অসাধারন নাটক আমাদোর কে উপহার দেবার যন্য ধন্যবাদ,0,entertainment
"সুন্দর কাজ, দৃশ্যায়ন নিয়ে বলছিনা, ঘটনা ও ও বয়েসের এই ক্রাইসিস কে তুলে ধরার জন্য ধন্যবাদ।",0,entertainment
অন্য মুবিরগান ডুকাইয়া দিছেন কেন,0,entertainment
পোবার গুদ টা কালো আমি দেখছিলাম মিনিটের,0,entertainment
নাদিয়া তোমার সাথে আমার পরিচয় শেয়ার করতে চাই,0,entertainment
এটা কোনো কথা !শুরুর সাথে শেষের বিন্দুমাত্র মিল আছে??<br />কমেডির নামে ভাঁড়ামি করছে। যত্তসব,0,entertainment
সৌভিককে দেখলেই গরুর হাটের কথা মনে পড়ে যায়।,0,entertainment
খুবি মিস করি বালাম ভাই,0,entertainment
"হুমায়ুন আহমেদ,তৌকীর আহমেদ,ফারুকি, তারেক মাসুদ এরকম হাতে গোনায় কয়েকজন পরিচালক আছেন যারা আমাদের ভালো ভালো মুভি উপহার দিয়েছেন।",0,entertainment
ভুল ভুল ভুল কেয়ামতের আলামত যে যার যোগ্য নয় তাকে সেইটা দিলেতো এমন টাই হবে। আরে ভাই তারা তো এই চ্যায়ারের যোগ্য না তাহলে এখানে বসার অধিকার কে দিয়েছে।,0,entertainment
অসাধারণ একটা ছবি আজ 15 বছর পরে দেখলাম আবার আমাদেরমাঝে অমর হয়ে থাকবেদিলদার ভাই,0,entertainment
নাটক টা যতটুকু ভালো লেগেছে তার চেয়ে বেশি খারাপ লেগেছেসংলাপ বুঝা না যাওয়ার কারনে।সংলাপের সময় সাইড থেকে বাজে আওয়াজ দেওয়া হয়েছে যা রিতিমত বিরক্তিকর।,0,entertainment
ওর বাড়ি রংপুর ওএকটি মফিজ,0,entertainment
এই ছবির অভিনেতারা এখন কোথায় আছেন? কেউ কি জানেন? বা তাদের দেখতে কি রকম?,0,entertainment
"নাটক এবং টেলিফিল্মের স্যুটিং- এর জন্য খুবই সুন্দর একটি জায়গা।নিজ চোখেই দেখুন <a href=""https://youtu.be/2QFlqKLXPbk"">https://youtu.be/2QFlqKLXPbk</a>",0,entertainment
মোশাররফ করিমকে একটুও মানায়নি😐,0,entertainment
পতিতা বউ পর্ব ৮ চাই<br />Very very nice,0,entertainment
গ্রামের নটকতো ভালোই লাগবে,0,entertainment
"বাংলা সিনেমার সবচেয়ে বড় ভিলেন হুমায়ন ফরিদি,ঠান্ডা মাথার গুন্ডা।",0,entertainment
বার বার দেখেন ভিউ বারান ভাইরাল করেন !! আবার গালি গালাচ ও করেন !! তারা গালি খায় খায় তিভু ভিউ তো পায় !!!!! সত্যি কথা আমরা বাঙালী পারি গালা গালি করি সমালোচনা এভাবেই গান বানা সবি একি গান সবি সুন্দর তগোরে এখন গারাব পা তাইন্না ছিরাবই ছিরাব,0,entertainment
সত্যিই আবাল..সময়টাই নষ্ট👿,0,entertainment
ইলিয়াসকানচন ও শাবনুরের কোন সিনেমা একসাথেদেখেনি এটাইপ্রথম সিনেমা কেন তারা একসাথে সিনেমাকরে নি????,0,entertainment
এই সব বিচারকদের পায়ের নলি কেটে দেওয়া উচিত বাইরে বের হলে এই সব আবাল মার্কা বিচারক যে করছে সে শালাও আবাল,0,entertainment
নাস্তিক দল জাহান্নামে যাবে কুকুরের দল নাস্তিকের বাচ্চা,0,entertainment
এরা মিহিলাকে সুচিত্রা সেন বানায় দিসে,0,entertainment
"ব্যাক্তিগত একটা স্টাডির পর বুঝলাম আজ পর্যন্ত যতগুলো বিষয় মনে মনে অপছন্দ করতাম সেগুলোই ঘুরেফিরে কোন না কোনভাবে একসময় আমার জীবনে এসেছে।<br /><br />তাই ভাবছি যে, এখন থেকে কিছু কিছু বিশেষ পছন্দকে মনে মনে অপছন্দ করা শুরু করব।।😆",0,entertainment
জাহিদ হাসান মানে সুপারহিট নাটক ।জাহিদ হাসানের পুরানো দিনের নাটক গুলো দেখার মজাই আলাদা ।জাহিদ হাসান মানে অসাধারন নাটক ।জাহিদ হাসান মানে অসাধারন অভিনয় ।,0,entertainment
আপনারা যারা উনাকে গালি দিচ্ছেন উনার আসল পরিচয় আপনারা জানেন জানলে হয়ত গালি দিতেন না। উনি একজন নাম করা পরিচালক। উনার অসংখ্য নাটক আছে।তার মধ্যে “হাউসফুল” পর্ব নাটক টা অসাধারণ। উনার মেকিং জাস্ট দেখার মত।আর উনি হাজারটা মাসুদ রানা তৈরি করতে পারেন।কারন একজন পরিচালক রাস্তার ছেলেকে সুপার হিরো বানাতে পারে।উনার যোগ্যতা আছে বলেই উনি বিচারকের আসরে বসেছেন।উনি পরিচালক উনি জানে কাকে কোন চরিত্রে মানাবে উনি হয়ত সরাসরি উনার মন্তব্য প্রার্থীকে বলে দিছে আর তাতেই সবার গায়ে লাগছে।আর বাকি বিচারক গুলা যে টাকা খেয়ে তলে তলে বিজয়ী ঘোষনা করে দেয় তখন গায়ে লাগে উনি ইফতেখার আহমেদ ফাহমি।উনার নাটক সিরিয়াল ড্রামা টেলিছবি গুলা দেখে উনার বেপার মন্তব্য করিয়েন।উনি একটা ভুল করেছে বলে উনি ফালতু এই ধরনের কথা থেকে সরে আসেন।,0,entertainment
এতো মানুষের সাথে নিজ তলা ভারা দিছে জে লজ্জ সরম কিছুই নেই।এটা হিরো আলোম এর ও জগ্গো নয়।হিরো আলোম নয়,0,entertainment
"অসাধারণ সিনেমা! সোনালী দিনের চলচ্চিত্রগুলো দেখলে প্রাণটা জুড়িয়ে যায়। এই সিনেমার একটি গান &quot; আমার এই গানখানি যদি ভাল লাগে, কোনদিন ভুলে যেও না&quot; সেসময়ে অসম্ভব জনপ্রিয়ছিল। আজও কানে বাজে গানের কথা ও সুরের মূর্ছনা। ভেজাচোখ সিনেমাটি অনেকের প্রিয় চলচ্চিত্র। সিনেমাটি আপনাদের সংগ্রহে কিংবাকি কারো কাছে আছে?",0,entertainment
হুমায়ুন ফরিদির অভিনয়ের কাছে সবার অভিনয় ফেইল।,0,entertainment
এগুলাকে বলে নাটক,0,entertainment
ভাই তারা তারি দেন।,0,entertainment
ক্যমেরাম্যান কি গানজা খাইছে নাকি,0,entertainment
ফিল্ম জগতের মেয়েরা একটাও ভালো না সব নষ্টা মাইয়া,0,entertainment
একেই বলে বস,0,entertainment
দেখাযাক কেমন হবে,0,entertainment
ওই একটা সময়ে আমরা নিঃসন্দেহে বলিউডের সাথে কম্পিটিশন করতে পারতাম। আজ আমাদের কোন অবস্থান নাই।,0,entertainment
"ভাইয়া তোমার মুচকি হাসি টা খুব বেশি সুন্দর মাশাআল্লাহ,",0,entertainment
সময় নষ্ট করলাম 😠,0,entertainment
আমার হিরো সাকিব খান,0,entertainment
ছবির নাম হওয়া উচিত নীচ তালা ভাড়া দিয়া ওপর তালা গড়ব। অথবা দুধের পাহাড়।,0,entertainment
আল্লাহ কে ভয় কর মরতে হবে এই দুনিয়াতে আজীবন থাকতে পারবেনা মরতেই হবে,0,entertainment
ইসলামের বিষয় নিয়ে মজা করা ঠিক নয় দ্বিতীয়বার এই ধরনের নাটক না বানানো হয় তাই আজকের মতো বাজে কমেন্ট করলাম না 👹👹👹👹,0,entertainment
আমিন খানের সাথে মাহিয়া মাহি জুটি হলে চরম হতো ...কোথাকার আবুল মার্কা টুকাই ধরে নিয়ে আসছে এই জন্য সিনেমাটা দেখবো না ....আমিন খান বেস্ট ওর কাছে শাকিব খান ও কিছু না ...,0,entertainment
এইগুলা কি বিচারক আমি অবাক হই ওদের ভাষার কি অবস্থা এইভাবে অপমানিত করার জন্যকি এই আয়োজন করার কোন দরকার ছিল,0,entertainment
এই যুগ এইরকমে কারো দিকে😅করেনা,0,entertainment
অনেক দিন পর আবার ও দেখলাম অনেক ভালো লাগলো,0,entertainment
ইচ্ছা করতেছে জংলি চুলওয়ালা জাজটাকে জুতা পিটা করি।,0,entertainment
ভাই এই ছবিটি অন্য চেলেনে আছে যদি পারেন তাহলে কিছু আন কমান ছবি দিন ভাই,0,entertainment
কারা কারা হাত তোল আগে কমেন্ট পড়ে তারপর নাটক দেখা শুরু করচেন,0,entertainment
বেপরোয়া(ইলিয়াস কান্চন) সিনেমার গান দিবেন অনুপম সিরিস,0,entertainment
ধন্যবাদ দিয়ে আমি ছোট করতে চাই না বঙ্গ এমন একটি নাটক উপহার দেওয়ার জন্য।<br />এটি শুধু একটি নাটক নয়।<br />এটি মানুষের অন্তরস্থল কে ছুঁয়ে যায়।,0,entertainment
"বুঝা উচিত ছিল এটা আর কেউ নয়,,,ফারহান ভাই",0,entertainment
সব ধর্মের উপরে মানুষ হলো একটাই ধর্ম। 🙏,0,entertainment
"রুবেলের,, জজ সাহেব,, পলাতক আসামী,, কাঙালী রাজা,, এই ছবি গুলো যে কোন একটা ছবি দেবেন কি ভাই",0,entertainment
কি দিনকাল আইলো জাম্বুরা দিয়াও ফেমাস হওয়া যায়। আর হিরো আলমের সাথে ওর মানাবে ভালো এমপি কি চো দিলে হওয়া যায়,0,entertainment
বিচারক নামে কলঙ্ক এরা,0,entertainment
বদমাশ মহিলা বলে উনি ৩০ পারা কোরআন হাফেজ<br />তাহলে উনি ওনার মেয়েকে নিয়ে গার্মেন্টস বা অন্যান্য কাজ কেন করল না ?,0,entertainment
"জগি টাকূর মুভি দেন ব্রাদার, অনেক খুশি হব।",0,entertainment
"অসাধারণ মুভি বাস্তব চিত্র দরে তুলেছে মুভি টি,, পুরুষ নষ্ট হয় নারীর কারণে, আবার খারাপ পুরুষ ভালো হয় নারীরি কারণে, সত্যি মুভি টি দেখে চোখের পানি দরে রাখতে পারলাম না, তোমার প্রত্যেক টি মুভিই বাস্তবে অনেক কিছু শিখিয়ে দেই ,, love you shalman sha,, জানিনা কবরে কিভাবে আছো তবে হে আল্লাহর কাছে দোয়া করি তোমাকে যেনো জান্নাত বাসি করেনআমিন..",0,entertainment
অবশেষে তাহলে পেলাম বসের সন !!!! লাইব টেকনোলজী,0,entertainment
কিয়ামত মনেয় হয় খুবি কাছে। আবাল একটা পাগল ছাগলে দেশ বরে জাচ্ছে,0,entertainment
"কিছু কিছু, নাটক, মানুষের জীবনে এতটাই মিলে জায় য়ে,, চখে পানি চলে আসে,",0,entertainment
"ভালবাসা এমনই হওয়া চাই,,,",0,entertainment
সাবিনার ফেইজ আল্লাকতো সুন্দরদিছে এমন একটা বউ পাইতাম আল্লার কাছে হাজার বার সুকুরিয়া করতাম সবসময় তাকে,0,entertainment
জাতির কাছে আবেদন ইফতেখার ফাওমী সাফায়েত মানসুর রানা শবনম ফারিয়া মমো মোস্তফা কামাল রাজ এই পাচ জন কে ভালো করে চিনে রাখুন। এই ধরনের বিচারক আমাদের দেশের জন্য লজ্জাজনক। তাদের চিত্র জগতের সবকিছু বয়কট করুন। যেনো আর কখনো কোনো কেউ আমাদের ভাইদের কে এভাবে মানুষিক নির্যাতন করতে না পারে।,0,entertainment
খুব সুন্দর মুভি শাকিব অপুু।,0,entertainment
বিচারক তোরা একটাও উপস্থাপক মেয়েটির জুতার সমানও সম্মান দেওয়া শিখলি নাহ।,0,entertainment
আমার জীবনের সবচেয়ে স্মরনীয় ছবি,0,entertainment
প্রিয় গানের তালিকায় আসমানী পিরীত গানটা আজ যুক্ত হলো<br />২০১৯ সালের সেরা গান,0,entertainment
নকল করেও ঠিক করে সিনেমা করতে পারে না নায়কের ওভার একটিঙ আর <br />ভিলেনের ফালতু চিৎকার সিনেমার <br />রুচি নষ্ট করে দিয়েছে,0,entertainment
আমি হতভাগা 😔<br />আমার কোনো বোন নেই 😭,0,entertainment
ইসলাম নিয়ে মজা করা ঠিক হয় নাই।পরিচালিত কে বলছি আগামী ইসলাম নিয়ে এমন জোক করা নাটক বানানো থেকে বিরতে থাকার জন্য অনুরোধ করছি।,0,entertainment
সেই সোনালী যুগের সেই সোনালী যুটি।আর হবেনা বাংলাদেশ এই রকম সিনেমা ও এই রকমের যুটি।,0,entertainment
খুব ভালো গানটা,0,entertainment
আমি মশাররফ করিমের নাম্বার ওয়ান ফ্যান রে পাগলা<br />♥♥♥♥♥♥♥♥♥♥,0,entertainment
পাগল,0,entertainment
এত লম্বা ভিডিও দেয়ার জন্য আপনাকে। কেয়া কসমেটিক এর পক্ষ থেকে থাকছে মাসুদ রানার ধ্বংস পাহাড় বই আর কিছু চারা গাছ। ওয়ালাইকুম আসসালাম।😇,0,entertainment
অসংখ্য ধন্যবাদ প্রিয় ভাই আপনাকে।,0,entertainment
সেরা অভিনেতা চঞ্চল চৌধুরী বাংলাদেশ,0,entertainment
আমার কাছে এই ছবির সুর অনেক ভালো লাগে,0,entertainment
ছবি সেস না হতেই সমাপ্ত সেটা আবার কেমন?,0,entertainment
আমি সুন্দর মনের মেয়ে চাই=974=77668805এমু,0,entertainment
বিচারকদের থেকে নবাগতদের অনেক ভালো দেখা যাচ্ছে জুতা মারা যান উচিত এই সালাদের,0,entertainment
সামাজিক একটা চবি অনেক সুন্দর হয়েছে।,0,entertainment
রিয়াজ শাবনুর রিয়াজ পূর্ণিমা মানেই রোমান্টক জুটি এ জুটির মুভি আমাদের কাছে চির দিন বেচে থাকবে,0,entertainment
গানটা শুনলে অনেক কিসু মনে পরে যায়,0,entertainment
আল্লাহ তুমি এদের হাত থেকে ইসলামকে বাচাও😥,0,entertainment
জমিম সেরা নায়ক,0,entertainment
"এইরকম মুভি কি আর হবে না,বাংলাদেশে",0,entertainment
অনেক দিন পর সেই রকম একটা নাটক দেখলাম।,0,entertainment
গান গুলো খুব সুন্দর।,0,entertainment
"পরিরে পরিরে আমারে না, আমারে খুব ভালো লেগেছে",0,entertainment
অনেক চেষ্টা করে ও চোখের পানিটা ধরে রাখতে পারলাম না,0,entertainment
"শুধু শাবনূর এর জন্যই মুভিটা দেখা,মিডিয়া জগতের সম্রাগী শাবনূর নুপূর",0,entertainment
ওরা কারা জারা ভালো খারাপ না বুঝে শুদু আনলাইক মারে 😬😬,0,entertainment
হা হা হা।মজা পাইলাম,0,entertainment
ফাহামি মমো আর ডিম পাড়া মুরগী ফারিদা এদেরকে সেফাতউল্লার কাছে পাঠানো হোক,0,entertainment
দেখতে বয়স্ক হলেও তেজ এখনো কমেনি,0,entertainment
অনেক অনেক ভালো ভাই এমন জদি সবাই হতো তবে আমাদের দেশটা আরো ভালো হতো,0,entertainment
আমাকে যদি কেউ খুশি করতে পারে আমার স্বামী বিদেশ থাকে আমাকে এড কর,0,entertainment
সত্যি ছবিটা অনেক সুন্দর,0,entertainment
ভাই তুমি নিজেকে কন্ট্রোল করলে কিভাবে,0,entertainment
তার দুধ দেইখা আমার বউ পাদ দিছে,0,entertainment
শেষ পযর্ন্ত দুই জনের সাথেই লিভ চুগেদার করে জীবন চললো <br /><br />নাটকের চরিত্র গুলো বাস্তবিক ছিল <br />কিন্তু শেষে দুই জনের সাথেই এটা মেনে নেয়া যায়না,0,entertainment
পরিচালক কে জানায় ধন্যবাদ।। এতো সুন্দর ছবি দেখানোর জন্য,0,entertainment
কাটপিস মুভি টা দেবেন,0,entertainment
সালমান শাহ সবচাইতে বেস্ট ডায়লগ ছিল এই ফিল্মে,0,entertainment
ভাই লাওয়ারিশ ছবিটা দেন না,0,entertainment
ও পাগল হয়ে গেছে,0,entertainment
দয়া করে পর্ব গুলো তাড়াতাড়ি দিয়েন ✌😢 রিকুয়েষ্ট,0,entertainment
ক্যামারা মাসুম খান ভাই,0,entertainment
"খুবই সুন্দর ছবি,সাকিব খান এর ছবি ভালো লাগে 😀",0,entertainment
ভাই আপনার ভিডিওর জন্য অপেক্ষা করতেছিলাম একটু দেরি দেরি করে আপলোড করলেন কেন,0,entertainment
"বড় ভাই শাবানা ,রাজ্জাক,ইলিয়াস কাঞ্চন ও দিতির স্বাধীন মূভি, রাজ্জাক মৌসুমি ও রুবেলের জজ সাহেব মূভি,রুবেলর বিচারপতি মূভি ও মালা তুমি কার মূভি গুলোদেন",0,entertainment
সাবনুরের বাবা মিশা মজা পাইলাম,0,entertainment
ছবিটা ভালোই তবে এখানে আমিন খান জানতে পারেনি যে নায়কা তার সত বোন নয়,0,entertainment
অশিক্ষিত মূর্খ বেয়াদব বস্তি থেকে বেড়ে ওঠা একটা ছোটলোক যখন বড়লোক হয় তখন এই রকম বলদ মার্কা বিচারক বাংলাদেশে তৈরি হয়।,0,entertainment
কাওরে গান টা শুনাইলে ঝাইড়া দোউর দিবো 😆😆,0,entertainment
বাংলার চলচিত্রের নিভে যাওয়া এক নকক্ষেত্র সালমান সাহ,0,entertainment
পপি আপু আমার অনেক পছন্দের একটা নায়িকার এই ছবিটা তো আমি অনেক ভালোবাসি আই লাভ ইউ পপি আপু,0,entertainment
খুব সুনদর এই ছবিটা শাকিব ওঅপুর জুটি তোতো ময়না,0,entertainment
পরিচালক কে পিটাইতে ইচ্ছা করলো নাটক দেখার পর ... বলদ পরিচালক,0,entertainment
রিয়াজের মত সুদর্শন নায়ক আর আসবেনা,0,entertainment
এত লেট করে দেন কেনো?,0,entertainment
বর্ষার গেন্জির আনারস দেখে মধুপুরের আনারস চত্তর এর কথা মনে পড়লো,0,entertainment
পতিতা পললী . হোম সারভিসে সুনদরী মেয়ে পাঠানো . হয় . যোগাযক করুন সুমন ভাই 01798558703,0,entertainment
"ফালতু নাটক। এ নাটকে গর্ভপাত দেখানো উচিৎ হয়নি।এমন করলে আল্লাহর শাস্তি অনিবার্য, যা শেষ অংশে দেখলাম।",0,entertainment
জামালপুরের সাধারণ জনগণের উচিত এদের দুজন কে জুতা পেটা করা।,0,crime
এর শেষ অংশ মিলে নি রিফাত হত্যার সাথে,0,crime
মধার চোদ তদোন্ত ইতো দেশটা খাইছে,0,crime
ভাই সবাই ভিডিওটা দেখেছে উনি বলছে হ্যাকাররা জড়িত মানলাম বাট আপনি এবং আপনার অফিস সহকারি দুজনই ছিলেন এক রুমে এখানে তো হ্যাকাররা যায়নি কিসের তদন্ত করবেন আপনি জনগণই তদন্ত করে ফেলেছে আপনি কেমন মানুষ ভালো তবে আমার মতে এই দুজনকে বিয়ে দেওয়া চলে কি বলেন আপনারা ভালোভাবে সংসার করতে পারবে একসাথে কেউ কোনো কথা বলবে না প্লিজ একটু ভেবে দেখবেন,0,crime
মিন্নি সম্পুন্ জড়িত,0,crime
মিন্নিকে আইনের আওতায় আনাহোক,0,crime
এক জনের জন্য এতগুলো মানুষের আহাজারি কেন যে। তোমরা অননাই পচর্দেয়। আজ যদি মানবতার কথা। ছিনতা করতা তাহলে তোমাদের এই দিনটা দেখতেনা। দুংখ জনক। আমি আপনাদের কে বলতে ছাই। এই খান থেকে শিখ নেন। আপনার ছেলে বা বাই ও বন্দু বানদকদের সাবদান করে দেন। অপকর্মের এটাই সাজা। পােপকোন দিন বাপ কেও ছাড়েনা।,0,crime
ধন্যবাদ আপনাকে দাড়ি থাকলে অসুবিদা ছিল,0,crime
আল্লাহ বাচাইচে কুন দাড়ি ওয়ালা নাই একটা দাড়িওয়ালা থাকলেও বলতো এটা জংগীদের কাজ এরাই রাজাকার আবাল সুদা নেতাগোর মন্তব্য কান জালা ফালা হয়ে জেত,0,crime
মিন্নিও দোষী,0,crime
মিন্নির ফাঁসি চাঁই,0,crime
আমরা এ র বিচার চায়,0,crime
তোরা মা জাতির কলক তদের পাথর মেরে হত্যা করা হোক,0,crime
তোদেরকে জুতা পিঠা করার দরকার মানুষের জিবন নিয়ে অভিনয় করিস,0,crime
ডিসি সাহেবের আইনত শাস্তি চাই,0,crime
এ লোকটির কোন লজ্জা নেই আবার সাংবাদিক সম্মেলন করেন ছি ছি ছি,0,crime
জুতার মালা গলাই দিয়ে সারা দেশে ঘুরাতে হবে।,0,crime
মিন্নির হাত আছে তাকে গ্রেফতার করা হোক।,0,crime
আমার মতে প্রতিটা পুলিশ যে কোন বড় ধরনের প্রভাবশালীদের পেছনে সিসিটিভি ক্যামেরা রাখা উচিত,0,crime
আমি ভারত থেকে বলছি বাংলাদেশের মানুষ কেমন ছি ছি দিনের বেলা এতোগুলি মানুষের সামনে কুপালো কেও বাছাইলনা,0,crime
অন্ন্য রকম একটা শান্তি পাচ্ছি মনে,0,crime
মিন্নি শতভাগ সাহসী। আর সে নির্দোষ। ভিডিওতে সেটা স্পষ্ট।,0,crime
আবারো বলতে বাধ্য হোচ্ছি আরও কয়েকটা অপরাধ ঘটেছে সেগুলোর এরম হওয়া দরকার আমি ইন্ডিয়া থেকে খুব ভালোভাবে উপভোগ করছি,0,crime
ধরাখেয়ে অসিকার,0,crime
কি ঘটছে এসব। আমাদের সমাজ ব্যবস্থা কত নিচে নেমে গেছে! হে আল্লাহ তুমি আমাদের সবাইকে উত্তম প্রদর্শন করো।,0,crime
দরা পড়লে আমাকে বাচাঁন,0,crime
প্রকিত আসামী মিন্নি,0,crime
সিরাজকে কি ডিম তেরাপি দেওয়া হয়েছে? জানলে কেউ জানাবেন `~,0,crime
মিন্নি জরিত আছে মিন্নি ফাঁসি হওয়া উচিত,0,crime
একদম ঠিক কথা বলেছেন ভাই যদি এই ডিসি সাহেবের যদি দাড়ি থাকতো তাহলে মহিলারা অনেক কিছু বলতো কেন যে সে দাড়িওয়ালা তাই,0,crime
তুমি বেছে থাক এলাকার পোলাপাইন তোমার আসা আছে,0,crime
হলে যেয়ে নিজের গায়ে আগুন দিয়ে আত্মহত্যা করবে বিয়াদপ লোক কি বলে কিছুদিন আগে এমন কান্না মেয়েটির পরিবার ও করছিল,0,crime
একজন মানুষ মরছে তা নিয়া সকলে কত। বিডিও। তৈরী হচ্ছে সবার মনে রং,0,crime
এরাতো নুসরাত তের খুনিনা এরা অনো কেছের আসামি,0,crime
খুনিদের পিতা মাতা পুরো বংশ গ্রেফতার করুন তাইলে ওরা আত্নসমপন করবে।,0,crime
আসলে দেশটা এমন যে জনগনের সামনে মানুষকে কুপিয়ে হত্যা করলেও জনগন বাচানোর চেস্টা করেনা কিংবা খুনিকেও আটকাইনা।তাই তো অপরাধীরা আরো অপরাধ করতে সাহস পাই।তাইতো দুনিয়া এত ধংসের পথে,0,crime
এইখানে কতগুলা বাঙালি পুরুষ ছিলেন এই কাজগুলা ইচ্ছা করলে রিফাত কে বাঁচাতে পারত কাপুরুষ গুলা দৌড়ে পালায়,0,crime
পাপে বাপকে ছারে না। সবাই সত্যের জয় চাই দেখতে,0,crime
এতোগুলো মানুষের সামনে মারল আর সবাই দাঁড়িয়ে দাঁড়িয়ে তামাশা দেখলো।।সাবাই যদি একসাথে প্রতিবাদ করতে পারতো তাহলে আজকে আর এইদিন দ্দেখতে হতো না😭।,0,crime
ডি ছি অখখম,0,crime
চাকরি থেকে বরখাস্ত করা হোক,0,crime
এই মেয়ে তোর কারনে মা বাবার আদরে ছেলেটা হারাইলো তোকে আল্লাহু তালা কখনো খমা করবে না,0,crime
হা হা হা এই রকম রুজ ঘটে সরকারি কর্ম কতারা সুযোগ পেলে কাউকে ছারে না,0,crime
ওরা সব অমানুষ এর দল এত মানুষ থাকতে একটা ছেলেকে কুপিয়ে মারছে কেউ বাছাই না হাইরে মানুষ এটাই কি মানবতা??😢😢😢,0,crime
হ্যাকাররা আমার ইজ্জতহানি করেছে আমি এর সুষ্টু বিচার চাই মাননীয় প্রধানমন্ত্রীর কাছে যেমন সরকার তেমন তার রক্ষক !,0,crime
ভেঘ কি?,0,crime
বাস্তবের সাথে ই মিল হয়নাই আর অভিনয় একদম বাজে হইছে,0,crime
এমন মাল টাই তো দরকার,0,crime
বাস্তব কথা,0,crime
ডিসির সাথে মহিলাকে বিয়ে পড়িয়ে দেওয়া হোক এটাই সঠিক বিচার,0,crime
আমি বাংলাদেশ পুলিশ কে বলবো আপনারা আগে মিন্নীকে রিমান্ডে দিন তাহলে অতি তারাতারি সব বেরিয়ে আসবে!!,0,crime
জামালপুর এর কন্যারা অনেক আত্নত্যাগী হয়৷,0,crime
আমারাও খুশি,0,crime
এই ডিসি যে মিথ্যা কথা বলছেন তা উনার চেহারায় ফুটে উঠেছে,0,crime
এই মেয়ে মিথ্যা কথা বলছে তাকে পুলিশ হেফাজতে নেয়া উচিত যখন কুপিয়ে মারছেন তখন তার হাতের ব্যাগ কিন্তু তোর সে হাত থেকে ছাড়ে নাই এর কারন কি সে এত স্বাভাবিক কেন,0,crime
এর আবার বাঁচার ইচ্ছা থাকবে কীভাবে এর তো বাঁচার অধিকারই নেই বাঁচার ইচ্ছা পোষণ করবে কিভাবে ইসলামের দৃষ্টিতে দু জনকেই পাথর নিক্ষেপ করে মৃত্যুদণ্ড কার্যকর করা উচিত,0,crime
আসলে হতভম্ব হওয়ার কথা যারা খুন করেছে তাদের বিচার হওয়া জরুরী মিন্নির বিচার সেটা হলো দুই স্বামীর ঘর করত,0,crime
খুব সুন্দর আপনার গান,0,crime
হায়রে পৃথিবী একজনকে জঘন্য ভাবে কুপিয়ে যাচ্ছে আর এতো গুলা মানুষ দাড়িয়ে দেখছে।।ভিডিও করছে।।।।হাতে তালি তাদের জন্য। । । 👏👏,0,crime
ঠিক কোই চেন বাই মেয়েটা দুস,0,crime
নির লজ্জো বাঙালি,0,crime
বাস্তব আর নাটক অনেক ডিপারেন্স আছে বুঝেছেন,0,crime
তাকে ফাসি দেয়া হক তার একাকার মানুষ কোথায় তাকে মেরাফেলা হক এরা হলো দেশের বাইরাছ এই বিচার ভালো না হলে দেশে আরো খারাব হয়ে জাবে,0,crime
ভাই রে এবার ডিসিরে ছাড় পুরানো হয়ে গেছে ব্যাপারটা বুকে হাত দিয়ে বলেন তো আপনি আমি কতো টা ভালো পানিসমেন্ট পেয়ে গেছে এবার থাম ভাই,0,crime
ওই কাংখির পোলার লিঙ্গ কেটে ফেলা হোক।,0,crime
আমাদের এই স্বাধীন দেশে আল্লাহর আইন প্রনয়ন করা হোক,0,crime
আপনি যেই খেলা দেখাইছেন 😅😅😅,0,crime
আপনার আপলোড বিডিওটা তিনবার দেখার পর ভাল ভাবে শুনে বুঝে তার পর লেখতে বাদ্যকরলেন আপনি বলেছেন একজন মানুষ যতই অপরাধ করুক এরকম শাস্তি দেওয়া ঠিকনা।আরু বলেছেন জনেন না কি অপরাধ করছে।না জেনে কেমনে আপলোড করলেন?আর একবার কি ভেবে বলেছেন যে কেরুসিন দিয়ে আপনাকে আগুন দিলে কেমন লাগবে?একটা জেন্ত মানুষকে আগুনে পুরে মারাটা একটু ভেবে বলছেন?কে বলেছে আপনাকে এই বিডিও লোড দিতে?আরে ভাই আমি আপনাকে পেলে একটু আগুন দিয়ে দেখলাম ঐলে।নুসরাতের মৃত্যুর চেয়ে অনেক সহজ হবে তাদের মৃত্যু।,0,crime
সালার কি আজব নিজের নামে অভিযোগ আর নিজেই তদন্ত করবে 🤣🤣🤣🤣,0,crime
কি বলে ওরা আল্লা নাকি বিচার করবে আপনাদের ছেলেরা জামাই রা যে নিস্পাপ একটি মেয়ে কে আগুনে পুড়ে মারছে এগুলো কি কোন অপরাধ না কেমন লেগেছিল যখন মেয়েটির গায়ে আগুন লাগিয়ে দিল দুরত্ব এদের ফাসি কাযকর করা হক,0,crime
আমি প্রথম থেকেই বলছিলাম। অবশ্যই মিন্নি জড়িত।,0,crime
সত্যঘটনা তুলে ধরা হয়নি,0,crime
ভিডিও ধারণকারীর বিচার চাইলেন সাধনা স্যার আমার কোনো ক্ষতি করে নাই ! স্যার শুধু আমাকে একটু আদর করেছে !!,0,crime
সরকারের কাছের এর ফাঁসি চাই,0,crime
এই মহিলা ও আছে,0,crime
সত্যি ভিডিও টা দেখে অবাক হলাম! এতো গুলা মানুষ মধ্যে কীভাবে পারে এই ভাবে কুপিয়ে হত্যা করতে! আমি দেশের এক জন সাধারণ নাগরিক হিসাবে বুজতাছি দেশ টা শুধু যারা আওয়ামী লীগ এর আর বাকীদের কোন মূল্য নাই বনের পশুর মতো এই ভাবে মরতে হবে!!! আসুন আমরা সবাই মোবাইল নিয়ে ব্যস্ত না থেকে এই দেশটাকে আবার স্বাধীন করি এবং এই সব জানোয়ার দের কে যারা লালন পালন করে তাদের পা না চেটে বজ্র কন্ঠ সংগ্রাম করি!!,0,crime
রিফাত মিন্নি মধ্যে যখন বারবারি হচ্ছে তখন টুপি পড়িত একজন রিক্সা চালক খুব কাছ থেকে দেখেছিল উনাকে জিজ্ঞেস করলে সব বিষয়ে জানা যাবে।,0,crime
কি বিডিও বানিয়েছো কোনো কিছু মিলেনি সবি মিথ্যা বানোয়াট,0,crime
ডিসি করলে ইনজয় পাবলিক করলে ধর্ষণ হায়রে বাংলাদেশ বঙ্গবন্ধুর সোনার বাংলাদেশ!,0,crime
রিফাত হত্যায় স্ত্রী মিন্নি মুল হোতা। মিন্নিকে প্রকাশ্যে দিবালকে ফাসি দেওয়া হউক।,0,crime
মিনিটে দুটো জিনিস লক্ষ্য করলাম। মাইয়াটা অনেক পর্দাশীল ।এক মিনিটের জন্যে ও হিজাব খুলে নাই ডিসি সাহেব শুধু মাঠে দৌড়াদৌড়ি করে গেলেন ।ফাঁকা মাঠ পেয়েও গোল দিতে পারলো না।মনে হলো টাওয়ারের নেটে সমস্যা ছিলো। ★তবে ডিসি স্যার কে দ্রুত যৌন ডাক্তার দেখানো দরকার★,0,crime
জাতি ভিডিও দেখতে চায়,0,crime
নিশ্চয় এটা বিরোধী দলের কাজ।,0,crime
ভলার ভাষা নাই ‌এরি নাম ভাল বাসা,0,crime
বড় খুনি তো মিনিন ভিড়িওটা ভাল ভাবে দেখলে টের পাওয়া যাবে,0,crime
মুল খল নায়ক আয়েশা। বুকার মত মিড়িয়ারা কি বলে। রিফাত মারা যায় আয়েশার একবিন্দু কিচ্ছু হয় নাই। ওর চোখে একফুটাও পানি নাই। হাই আয়েশার ও ফাসিঁ চাই,0,crime
যেমন কর্ম তেমন ফল সে সময় মনে ছিলোনা আরেক জনের ভরসা করে কিছু করতে নাই বুঝলে আমি মহান আল্লাহ তায়ালার কাছে ফরিয়াদ করি যেন এদেরকে আখেরাতেও যেন জায়গা না হয় আর ফাঁসি কার্যকর অপেক্ষা আছি কি বলেন সবাই,0,crime
সেখ হাছিনা জাতির সাথে নতুন নতুন নাটক সুরু করেছে,0,crime
লাশ দেখতে চাই।।,0,crime
আমি নিশ্চিত বলতে পারি এই হত্যাকান্ডের সাথে মিন্নি জড়িত। মিন্নির আচরণে তা প্রতিয়মান।,0,crime
তারা তাড়ি ফাঁসি চাই,0,crime
তদের বিরুদ্ধে একশন নেওয়া হবে ত্বরা বাস্তবেই ইয়াবা ব্যবসা করিস।থানায় তদের নামে জিডি করা হয়েছে,0,crime
খুব ঠান্ডা মাথার জঘন্য অপরাধী এই মিন্নি।দুঃখোজনক হলেও সত্য উপর মহলের নোংরা রাজনীতির কারনে তার কিছু হচ্ছেনা আর হবে বলেও আমি মনে করি না। এসবের সঠিক বিচার একদিন আল্লাহ্ করবে আর সেই এদেরমতো মেয়েরা কোন মতেই রেহাই পাবেনা ইনশাআল্লাহ।,0,crime
সঠিক বিচার চাই,0,crime
বোঝা যাচ্ছে ভিডিওটি সবাই দেখছে তাহলে সেই অনাকাঙ্ক্ষিত মিনিটের ভিডিও,0,crime
কে জানিনা সত্তো বাই কি তবে জানি আল্লা আছেন বিচার হবে কতবেল একটানারীকে এতোটয় কষ্ঠ দেউয়াটা ঢিক না,0,crime
যে ভিডিও টা ভাইরাল করছে । তাকে সেলুট । এই ভাবেই মুখস খুলতে হবে।,0,crime
লুইচ্চামি করার ভিডিও থাকতেও তা খুতিয়ে দেখা লাগবে কেন,0,crime
সবই মিন্নির অভিনয়,0,crime
দেশে অনেক অফিস ও উর্দ্ধতন কর্মকর্তা আছে এ ধরনের লুচ্চামি করে,0,crime
ক্যামেরা লাগানো অপরাধ নয় বরং তাদের জাতীয় ভাবে পুরস্কৃত করা হোক।,0,crime
আমি বুঝিনা এই সামান্য ব্যাপারটি পুলিশের মাথায় আসছেনা কেন?,0,crime
সে নিজেই যে এই সবের সাথে জড়িত সেটি তার অঙ্গ ভঙ্গিতে স্পষ্ট হয়ে উঠেছে। এই সব অকল্যাণ কর ডিসি কে এই মুহূর্তেই চাকরির থেকে বহিষ্কার করে তাকে আইনের আওতায় এনে কঠিন শাস্তির ব্যবস্থা করার জোর দাবী জানাচ্ছি।।,0,crime
তদন্ত এটা আসলে বাহানা যেখানে প্রমান দৃশ্যপটে সেখানে তদন্ত বিবেচনা এগুলার দরকার কি সোজা শাস্তি না দিয়ে নটক করে জনগনের সাতে,0,crime
আমার কনো তদন্তত দেখতে চাই না কারন আজ প্রজন্ত কনো তদন্ত ফল পাই নাই তদন্ত আর কি করবে তদন্ত তো ভিডিও তেইতো দেখা যায় ডিসির কঠিন সাজত্তি দেওয়া হক এমন কি ওই মেয়ের ও,0,crime
ভাই আপনাকে ধন্ন বাদ সুন্দর ভাবে গুছিয়ে কথা বলেন।আপনার উপাস্থাপনা গুলো দেখি।ডিসি কেন অনেক উপর ওয়ালা লোক আড়ালের বাহিরে এসব করে যাচ্ছে।হয়ত ধরা যায় না।রাস্তায় ডাস্টবিনে পলিথিন বেগে বাচ্চা পাওয়া যায় এদের কারনে। আপনি দেখেন কিছুদিন আগে রাস্তায় ফুট ফুটে ডেলিবারি বাচ্চা নাভির রগ ছিরে নি। ফেলে দিয়ে চলে গেছে।এদেরকে বিচার কাঠ গড়ায় আনতে হবে।,0,crime
মানুষ অপরাধীদের খুঁজে শাস্তি দেওয়ার জন্য কিন্তু আমার আল্লা অপরাধীদের খুঁজে ক্ষমা করার জন্য,0,crime
মোটা করে রেকরেক গেঞ্জি ওইটা কে কিছু করা দরকার,0,crime
বাহ সাংবাদিক সহজ সরল মানুষ গুলারে কিভাবে প্রশ্ন করে!!!,0,crime
এক জন মেয়ে কে কি এত মানুষ মিলে খুন করছে আমার বিশ্বাস হয় না আজ কাল ভালো মানুষ সাজা বুক করে আর অপরাধী সারা পায়,0,crime
জন্ম গত সমস্যার কারনে মিন্নীর এমন অবস্হা মিন্নী কে এন কাউন্টারে ফেলা দরকার।,0,crime
আমার সোনার বাংলার খুনিদের বিচার হচ্ছে না বলেই এমন ঘটনা হচ্ছে,0,crime
তোমাদের কান্না দেখলে কারো মায়া লাগে না,0,crime
রিফাতে বৌ ওদের সাথে জরিত আছে,0,crime
মিন্নির এখানে হাত আছে পুরাই আমরা বুঝতাছি রিফাত কে যখন নিয়ে যাচ্ছে মিন্নি তখন খুব সাভাবিক ভাবে হাটতাছে এতে প্রমান হই মিন্নির হাত আছে,0,crime
এদের কান্না দেখে আমার খুশি লাগতেছে। আসামীদের ফাসিঁ কার্যকর যেনো তারাতাড়ি হয়,0,crime
পতিতা নারী বাধীরা কি এখন ঘুমাচ্ছে কোথায় আজ সুলতানা কামাল রা খুশি কবীর রা মুরগী শাহরিয়ার রা,0,crime
কোনটা বানানো ভিডিও তা মানুষ বুঝে,0,crime
সারাদেশ ফাসি দেখতে চায় কান্না কোনো লাভ নেই যত তারাতাড়ি মেনে নিবেন তত ভালো,0,crime
বাই আমি এই ভিডিওটা অনেক বার দেখিচি আমার মতে এই মেয়েটার কারনে রিফাত খুন হয়েচে কারন মেয়েটা জদি প্রথমে চলে গেলে আর এমনটা হতোনা বাই আমি প্রথমে মেয়েটার বিচার চাই,0,crime
এই হত্যা সাথে মিন্নি জড়িত আমার মতে মিন্নিকেও আসামি করা হোক তাহলে সব কিছু বের হয়ে জাবে,0,crime
মাননীয় সাহেব আপনি তো অনেক দুর্বল,0,crime
শিক্ষা হওয়ার দরকার।।।,0,crime
আকাম কইরা কিসের বিচার চাস।আজ তোদের বিচার না হইলে দেশের অন্য জব গুলতেও দেহ ব্যাবসা হবে,0,crime
দৃষ্টান্ন মূলক শাস্তি চাই,0,crime
বাংলাদেশের আইন সব চেয়ে ভালো কাজ করবে।ফাশি হলে,0,crime
নয়ন বন্ড অাগেই প্রান দি। অাসল কালপ্রিট রিফাত ফরাজি।,0,crime
এখন আর কি হবে নুসরাতের গায় আগুন দিতেসময় মনে ছিল না।। কিছু কররা নাই,0,crime
🍌 খেয়েছে কে আর 🍌 প্রদানকারীর আজ কি হাল ! 😂 বাংলাদেশ সত্যিই বহুদূর এগিয়েছে ! 😁,0,crime
এতবড়ো একটা সত্য ঘটনাকেউ মিথ্যা বলে চালানোর চেষ্টা করছেন আপনারা। এটা মিনিটের ভিডিও না মোটামুটি মিনিটের একটা ভিডিও।,0,crime
প্লিজ পরিবেশটা সুন্দর না!!হূ হূ কোন হৈইচৈয় আছে!! না না ভিডিও দেখিইইই একটু দেখিইইই। আপনারা দেখবেন 🤣🤣 করেন,0,crime
লালমনিরহাটের জেলা জজ মাস থেকে নেই।প্লিজ এ নিয়ে কোন প্রতিবেদন করুন,0,crime
আমি বলছি তার ইস্তী কে আইনের করা শাস্তি দেওয়া হোক।,0,crime
মজা তুমিও পাইচো সারেও পাইচে ঠিক আচে,0,crime
ঠিক,0,crime
ইসলামের আইন মোতাবেক ওর শাস্তি একমাত্র মৃত্যুদন্ড,0,crime
রিফাত কে আল্লাহ যেন বেহেস্ত নসিব করেন,0,crime
ভাই আমিও দেখেছি,0,crime
তার জন্য কাছে সারা দেশে চাকরি দরজা খোলা,0,crime
লা হাওলা ওয়া লা কুয়ালাতা ইল্লা বিল্লা এগুলো এডিটিং করা যায় 😁😁😁😁😁,0,crime
আজব দুনিয়া,0,crime
অপস্তাপিকা আপু আপনার কাছে কতো মিনিট এর ভিডিও আছে আমার কাছে মিনিট এর ভিডিও আছে,0,crime
আমরা মিন্নির ফাঁসি চাই আর যারা ওর সাথে ছিল তাদের সবার ফাঁসি,0,crime
দয়া করে সবাই মিনিট এ দেখুন রিফাত ও মিন্নি দূর থেকে মনে হয় কিছু বলছিল।এই মিন্নি মেয়েটা পুরা জরিত ওকে কেন পুলিশ এখনো ধরছে না।ও ব্যাগ তোলা আর জুতা পরছিল ওই সময় কোন বউ কি তার হাসবেন্ডকে ওই অবস্থায় রেখে এ সব করতে পারে!,0,crime
এতো দেরি করছে কেন। কুকুর মারতে এতো দেরি করতে হয় না।,0,crime
অভিনয়,0,crime
দেশে রিফাত নুশরাতের বাবা মায়ের মত আর কারো বোক যেনো খালি না হয়,0,crime
? থেকে ? সময়ের মাঝখানের সময়টুকুর ভিডিও ক্লিপ কোথায়?? ঐ সময়ে কি হয়েছিলো যে কেটে বাদ দেয়া হলো???,0,crime
রিফাতের স্ত্রীর গতিবিধি সম্পূর্ণ সন্দেহজনক। হত্যাকারীরা রিফাতের স্ত্রীকে আদরের সাথে সরিয়ে রিফাতকে কোপাচ্ছে। যখন রিফাতকে নিয়ে যাচ্ছে তখন তার স্ত্রী তাদের সাথের একজনই মনে হচ্ছে। কোন প্রতিক্রিয়া নেই। তার স্বামীকে ধরে নিয়ে যাচ্ছে সে ধীরে সুস্থে এগিয়ে যাচ্ছে তাদের সাথে সাথে। তিনি স্বাভাবিক ভাবেই তাদের অনুসরণ করছেন। যেন এমনি হওয়ার কথা ছিল।,0,crime
ফাসি হয়ে গেছে নাকি মিথ্যা কথা লেখছছ কেন তুই,0,crime
তবে গান টা কিন্ত খুব ভাল গেয়েছেন।,0,crime
এ মেয়েটার ফাঁসি চাই,0,crime
এইগুলো এডিটিং করা জায় 😁😂🤣,0,crime
আমাদের প্রধানমন্ত্রী কে বলছি দুরত্ব ফাসির রায় কাজকর্ম করা হক।এইসব কান্না দেখে ভাংগে পরবেন না,0,crime
আমি শিওর ও ওর মেয়ের সাথেও এ কাজ করছে,0,crime
যে অপরাধী সেই করছেন তদন্ত । এর চেয়ে নিকৃষ্ট জগন্য এবং হাস্যকর ব্যাপার দ্বিতীয় টি নেই । যেমন সরকার তেমনি তার কর্মকর্তারা । গুড ভেরি গুড ।,0,crime
ছি ছি ছি ছি ধিক্কার জানাই ধিক্কার রাষ্ট্রের দায়িত্ব নিয়ে অবহেলা ও অপকর্মে লিপ্ত হওয়ার দায়ী এ ডিজিটাল ধর্ষকের শাস্তি দিতে হবে সারা জীবন জন্য বহিষ্কার করার হোক সাসপেন্স করা হোক চাকরি থেকে এখন দেশের যারা অপরাধ করছে তারা সবাই রাষ্ট্রের সকল সুযোগ সুবিধার ভুগ করে তারা অপকর্মে লিপ্ত রাষ্ট্রের কি তাদের বাবদাদা জমিদার সম্পত্তির নাকি যেমন খুশি তেমন করে যাবে অাইন সবার জন্য সমান হতে হবে,0,crime
দুই জনেরই সমান অপরাধী দুই জনেরই বাচ্চা সন্তান আছে কেনো এই কাজটি করলেন,0,crime
সব কিছু তো করছে এম পি পুএ,0,crime
এভাবে যদি প্রতিনিয়ত সকলের সামনে প্রকাশ্যে মানুষ হত্যা হয় আর তার যদি কথা থাকে একটাই যে আমরা তাকে আইনের আওতায় আনবো তাকে পর্যাপ্ত সাজা দেবে এটা কোন সাজার মধ্যে পড়ে না আমরা সাধারন মানুষ একটা জিনিসই চাই এরকম হচ্ছে আর সেগুলো যদি সাজা হয় জেল হয় তাহলে তারা অবশ্যই প্রশ্রয় পাবে তারা যেভাবে মানুষকে প্রকাশ্যে হত্যা করছে ঠিক তেমনি তাদেরকে আইনের আওতায় এনে প্রকাশ্যে গুলি করে হত্যা করা হোক যাতে পরবর্তী কেউ এসব করার সাহস না পায়,0,crime
ফাঁসি দিয়ে কারো আত্মার শান্তি দেওয়া যায় না তাদের যাবজ্জীবন কারাদণ্ড দিলে আমি মনে করি ভালো হতো একজনের জন্য অনেকগুলো পরিবারের ক্ষতি হবে,0,crime
খুন এর সঙ্গে মহিলার কোন সম্পর্ক নেই মহিলা তার সমস্ত শক্তি দিয়ে চেষ্টা করেছে তার স্বামীকে বাঁচানোর জন্য এটাই সত্য যারা মহিলা কে ফাঁসানোর চেষ্টা করতেছে তাদের খুঁজে দেখতে হবে তারা এদের সঙ্গে জড়িত আছে কিনা এটাই সত্য নয়ন ছিল মাদকাসক্ত সন্ত্রাসী সে জানতো নয়নের সঙ্গে যদি আমার বিয়ে হয় তার সঙ্গে আমি জীবন কাটাতে পারব না তাকে নিয়ে সুখী হতে পারব না তাই বাই এন কে দূরে সরিয়ে রিফাত কে বিয়ে করেছে কিন্তু রিফাত তোর সঙ্গে বিয়ে হওয়ায় নয়ন সহ্য করতে পারেনি তাই খুবই দুঃখজনকভাবে তার বন্ধুদের নিয়ে এই হত্যাযজ্ঞ তাণ্ডব চালায় মেয়েকে ফাঁসানো মোটেও ঠিক হবে না মেয়ে বিয়ের আগে অনৈতিক কার্যকলাপ অনেক করেছে সে যে ভাগ সতী সাধ্বী নারী সেটা কিন্তু নয় কিন্তু যা করেছে বিয়ের আগে করেছে বিয়ের পরে এই সমস্ত কিছু ত্যাগ করেছে এবং তার স্বামীকে নিয়ে এসে সুখী ছিল ভালোই ছিল কিন্তু এটা নয়নের সহ্য হচ্ছিল না তাই রিফাত কে সে দুনিয়া থেকে সরিয়ে দেয় মেয়ে নির্দোষ নির্দোষ নির্দোষ একশ ভাগ নির্দোষ মেয়ে যদি জড়িত থাকত মেয়ে যদি নয়নকে দিয়ে খুন করা তো তাহলে অন্যভাবে করাতে পারতো রাস্তায় নয় এবং মেয়ে সেখানে উপস্থিত থাকার প্রশ্ন আসে না এখানে মেয়ে সম্পূর্ণ নির্দোষ,0,crime
আকামের সময় সন্তানের দিকে তাকাও না এখন ধরা খাওয়ার পর সন্তানের কথা মনে পড়ে,0,crime
ধন্যবাদ আপনাকে ভাই সত্যি ঘটনা বননা দিলেন,0,crime
আমার ধুন ডা বানাও তুমরা বেরিয়া জা ইউটিউব থিকা মিন্নির দুশ টা তরাও গুপন করা ধরছছ তরা পুরুশ না,0,crime
সব সালাই ভালো এবার আমার নৌকা থেকে নামো।,0,crime
চোর কি কখনো বলে আমি চোর,0,crime
এখন বোঝেন নুসরাতের পরিবারের কেমন লাগছে।,0,crime
সরকার আগে অবশ্য জানে বড় অফিসার সকলে জড়িত তাদের ধরুন আইনের লোক আগে ও জানে লাইসেন সরকার এখন কেন ধরল মদ কোথায় বিক্রি করার হয় কেন বাংলাদেশে মদ তু ভালো না আইন কে আইনের গতিতে চলতে দিন অতপর তারা মোটা অংকের টাকা পায় এই জন্য দেশে আইন সঠিক না পুলিশ মুক্তিযুদ্ধা ক্লাবে কেন সরকার কি ?,0,crime
মেয়েটার চালাকি মনে করছে স্যার যদি নিদুশ হয় পরে মেয়েটা বাচতে পারবো এবং কি আরো মজা করতে পারবে,0,crime
আজও নুসরাতের মায়ের বকের ভিতর হা হা হাকার কুমিল্লা পাঠিয়ে ওদের লাস দেখতে চাই নুসরাতের মায়ের কাননা দেখে পুড়া দেশ বাসি কেদে ছিল আর তদের কাননা দেখে পুরা দেশ বাসি হাসি পায়,0,crime
তোর বিচার করতে হবে।।,0,crime
মেয়েটার ইচ্ছা বা অনিচ্ছা হোক সেটা বড় কথা নয় মহিলার কুপ্রস্তাবে একজন সম্মানিত ডিসি রাজি হওয়ার কারণে তারা দুজনেই সমান অপরাধ করেছে 😎😎বাংলাদেশে এই ঘটনার রাই দেখতে চাই✊✊,0,crime
সালা কি তদন্ত করবে একজন শিক্ষিত লোক হরে এতো কিচু করার পরেও বলে তদন্ত করতে এটাই বাংলার আইন,0,crime
খবরটা😮😣,0,crime
স্যার আপনার ক্ষতি করবে কেন স্যার তো আপনাকে মজা দিয়েছে,0,crime
কীভাবে এভাবে মিথ্যা কথা বলছ মিন্নি? এই ভিডিও থেকেই তো প্রমাণ হয় তুমিই দায়ী ? ?,0,crime
অভিনয় করে করে মিন্নী,0,crime
আমার কাছে এতটা খারাপ লাগলো যে রিফাত যাকে তো লাভ করতো ভালোবাসতো সে নিজের হাজবেন্ড কে হত্যা করল আমি চাই যে রে মিনির ফাঁসি হয় আমি না আমরা সবাই চাই যে রিফাতের হত্যার বিচার হোক,0,crime
মিন্নির ফাঁশি চাই,0,crime
আমাদেরও বউ আছে আমাকে কেউ এইভাবে ধরে নিবে সে খকনও দিবে না?,0,crime
বলের ভিডিও,0,crime
প্রথম আলো কি ফাজলামী করে?,0,crime
ভাই মেয়ের দোষ আছে,0,crime
মারার জন্য আগে থেকেই কিছু ছেলেদের কে একত্রিত করে ছিল।,0,crime
ছবি দুটির মধ্যে জামা এক হলেও 👂 কানের দুল আলাদা এবং চুলের ইষ্টাল আলাদা । তার পরেও দোয়া করি আল্লাহ যেন খারাপ মানুষের সঠিক বিচার করে আমিন ।,0,crime
রিফাত হত্যার ন্যায় বিচার চাই,0,crime
আফসোস লাগে হারাম খোরের দেশে জনমো আমাদের।,0,crime
মিনিট এর বিডিওটা কই লিংগ দেন,0,crime
বাস্ত বায়ন করা নাহলে ধরে নিতে হবে বর্তমান পরিস্হিতি ডান্ডা করতে সুধু রায় দেখানো হলো।,0,crime
সত্য ঘটনা জানা যাবে যদি মিন্নীকে জিজ্ঞেসাবাদে নিয়ে যাওয়া হই।,0,crime
আমার প্রশ্ন হচ্ছে এরা কি কখনও এদের কুকর্মের শাস্তি পাবে,0,crime
ডিসি খেলা পারেনা মিনিটেই মাল আউট হয়ে গেছে লাগাতে পারেনি সে ভালোভাবে ওরিজিনাল ভিডিও মিনিট ওটাতে কাপড় খোলা ও আছে মুখ পরিষ্কার দেখা যাচ্ছে,0,crime
আপনারা কি বুঝাইতে চাইতাছেন রে মিনি মেয়েটা কোন অপরাধে না আসলে মেয়েটা অপরাধী আপনাদের নাটক আমি পছন্দ করি লাম না ওকে,0,crime
কারা কারা খুশি হয়েছে এই ফাসির রায় শুনে দেখি সেই ফ্যান গুলো কে,0,crime
রিফাত এর স্ত্রী কিন্তু প্রথম থেকে যখন সবাই রিফাত কে ধরে মারতে মারতে নিয়ে যাচ্ছে তার স্ত্রী কিন্তু কিছুই বলে না।সে পিছনে আস্তে আস্তে হাঁটতেছে কোপানোর সময় রিফাতের স্ত্রী নাটকের অভিনয় করছে,0,crime
এতো গোলা মানুষ কেউ বাছানো জন্য আসলোনা,0,crime
এখানে যারা রাজনীতি ব্যাক্তি জরীত আছে আমরা তাদের ফাঁসি চাই ফাঁসি দিতে হবে,0,crime
মিন্নিকে ফাঁসি দেওয়া হোক,0,crime
চোর এর দশ দিন পুলিশ এর একদিন,0,crime
কত ধার্মিক মুসলমান😁 কাপড় খুলছে হিজাব খুলে নাই।,0,crime
গনদুলাই দেওয়ার দরকার,0,crime
সবার কি ফাসির কারজ্জকর হয়েছে,0,crime
হা হা হা মুক্তিযুদ্ধ রে তুরে বিক্রিকরে খুব মঝা পাইতেছে আওমিলিগ,0,crime
এই ডিসির ফাঁসি চাই,0,crime
উনাদের বাবার দেশ তাই লুটেপুটে খাচ্ছে যা ইচ্ছে তাই করতেছে।,0,crime
ধুরু খেলমু না। এরা দেখলো মিনিট আমি দেখলাম মিনিট। বাট হালায় কেলা পারে না 😂😂😂😂😂😂😂,0,crime
এক নাগিনির চুবলে দুই সাপুড়িয়া ধংশ হলো ইস কতো কষ্টের জীবন আল্লাহ জেনো রিফাত কে জান্নাত দান করেন আমিন👍👍👍👍💗💗💗💝💝💝💝 👇,0,crime
মিথ্যা কথা বলে,0,crime
রিফাত শরিফের স্ত্রী সে দুসি তার বিচার হওয়া উচিত,0,crime
লজ্জাও নেই অবাক হলাম!,0,crime
এরুকুম জারকদের সবার শামনে ফাঁশি হক,0,crime
আরে ভাই খুজে দেখেন আরো অনেক লোক আছে যাদের এমন ঘটনা আছে পদক ফেরত আনতে হবে তাহলে,0,crime
অনেকে কমেন্ট করছেন বউ সুন্দরী তাই ওই লোকের অপকর্ম করা ঠিক হয়নি আরো কতো কি। এর মানে কি যাদের বউ সুন্দর নয় তারা এই অন্যায় করলে দোষ নাই তাই তো !!! কি দৃষ্টিভঙ্গি আমাদের মেয়েদের বাহ্যিক সৌন্দর্য এর উপর নিভর্র করবে তার স্বামী চরিত্র 👌,0,crime
আহত স্বামির সাথে মিন্নি ক্যানো আসলো না???,0,crime
যোদি রিফাত ভাই বাইচা যাইতো তাহোলে ভিতরে অনেক শান্তি পাইতাম,0,crime
কিছুই বলার নাই সব কিছুর মূল রাজনিতি,0,crime
মিন্নি কতটা খারাপ ছিল সেইটা দেখান,0,crime
আসলে একটা মেয়ে ছোট থেকে বড় হয় মা বাবার কাছে বছর আর এই সময় টা তার কাছে তার বাবা মা ভাই বোন আপতিও সজন সবার পতি মহব্বত থাকে? আর পরে যখন তার বিয়ে হয়ে যায় তখন তার কাছে দুনিয়ার সব ছায়তে বেশি মহব্বত যার জন্য থাকে সেইটা হয়লো তার শামী? আর ওই মহব্বতের শামীকে কয়েকটা ভখাটে ছেলেরা মারতে মারতে নিয়ে যাচ্চে আর সে ছোট ছোট কদমে হাটতে ছে আর ভাবছিলো যে কেওতো দেখতে ছেনা আমার নাটকটা আমি আর একটু পরে শুরু করবো সে তো জানেনা নাটক শুরু করার আগে ক্যামরায় নাটকের ভিডিও শুরু হয়ে গেছে একটা কথা বলেনা যে সত্তিকে ডেকে রাখা যাইনা এইটা সেই সত্তি যেইটাকে ডেকে রাখা গেলোনা এ জন্য রিফাত হত্যার মুল ভিলেন মিন্নিকে জন সুম্মখে পাথর মেরে হত্যা না করলে এরকম আরো অনেক মায়ের বুক খালি হবে? আর একটা কথা বাকি থেকে গেলো সেইটা হলো যখন দেখলো তার শামীকে কোবাইতে শুরু আর তখন মিন্নি হাজির হয়লো কেন জানেন সে তো জানে এখন মানুষ পানিতে ডুবে মরতেছে গাডির নিছে পডে মরতেছে সন্তারাসিরা চুরির আাগাতে লাঠির আাগাতে মানুষ হত্যা করতে ছে আর সবাই ক্যামরা নিয়ে ব্যাস্ত কার আগে কে পোষ্ট করবে ফেসবুকে ইউটুবে এজন্য সে একটা নাটক করছিলো নিজেকে নিরদুষ পমান করার জন্য,0,crime
হাইরে বাংলাদেশ হেলাই হেলাই হওয়ে গেলো শেস দোনিয়ার মানুষের বওয়ে কতওয়েনা আবেগ দেখাই কিনতু আললাহর জাহাননামের বওয়ে আমরা কেও করিন্ হাইরে মুসল মান,0,crime
ডিসির ফাঁসি চাই দেখা যাক বাংলাদেশ সরকার এই ভেপারে কী বলেন যারা আমার সাথে একমত তারা অবশ্যই লাইক করবেন,0,crime
রাম দা আনল কার দোকান থেকে সেটা খতিয়ে দেখা উচিত,0,crime
আমার এই ফরাসির আসামিদের দেখে খুব খুব আনন্দ হচ্ছে যেমন কর্ম তার তেমন ফল আল্লাহ সবাইকে হুসিয়ার করে দিলো,0,crime
ভাই উনার ছুটির দরখাস্তে দেখবেন। এই মহিলার পদবি ডিসি সাহেবের গপন কক্ষের সহজগি।,0,crime
এই নারী শয়তানের চেয়ে খারাপ আইনের আওতায় আনা হোক। এই নারীকে,0,crime
মিন্নির প্ল্যান সব উপযুক্ত বিচার হোক,0,crime
লুচ্ছামি করবে আর সংবাদ প্রচার করবেনা তা কেন হবে,0,crime
ভাই এক কথায় অসাধারান গান,0,crime
মিন্নি একটা খারাপ মেয়ে এখন যে বিয়ে করবে সেও খারাপ ছেলে হবে,0,crime
আপনাদের ডিস্টার্ব এর কারনে আসল কামডাই করতে পারে নাই আহারে বেচারা 🤣😅😆😃😉,0,crime
এটা কখনো কাম্য নয়। একটা মহিলাকে তাড়া করে এভাবে ভিডিও করা। আপনারা না শিক্ষিত জাতি। পাপ করেছে। আপনাদেরও দিকে তাকান গোপনে কত পাপকাজে লিপ্ত হোন। তোবে এভাবে তার দিকে ধেয়ে যাওয়া কখনো কাম্য নয়।ভূল বললে ক্ষমা করবেন।,0,crime
তীব্র নিন্দা জানাই,0,crime
রিফাদের হত্য কারি তা ওয়াফ সবটা গটনা ছিল তার ওয়াইফের পরি কলপিত সিসি টিবিতে তাই দেখা যায়,0,crime
তোমার বাচ্চারা এখন বাচঁবে কি মুখ নিয়ে তর মতো মায়ের ঘরে যেনো আল্লাহ কোন সন্তান না দেয়!!,0,crime
হাহাহা এখন দেখি নতুন খেলে। আগে কই ছিলা জখোন কাম করছো তখন মনে ছিলো না।,0,crime
ঘটনা হয়ত এইটা হতে পারে মিন্নি সাথে রিফাত ফরাজি পারকিয়া ছিল কিন্তু তাদের পথের কাটা ছিল নয়ন ও রিফাত ভিডিও দেখলে বুজা যায় নয়নের থেকে রিফাত কে মারার জন্য রিফাত ফরাজি আগ্রহ ছিল মানে মিন্নি ও রিফাত ফরাজি মিলে এক দিলে পাখি মারার পরিকপনা করে রিফাত মাডার আর নয়ন ফাসি বা ক্রসফায়ার বেস ওদের রাস্তা ক্লিয়ার,0,crime
জখন নসুরাত,0,crime
রাজার দূষে রাজ্য নষ্ট প্রজা কষ্ট পায়। এ কথাটা যোগ যোগ ধরে মানুষ মুখে মুখে বলে আসতেছে। আর এটাই সত্যি। গনতান্ত্রিক দেশের গনতন্ত্র হারালে এর সাথে মানুষের মৌলিক অধিকারগুলোও হারায়। তখন সেখানে চলে আসে অরাজকতা পেশীশক্তি। সুতরাং যতদিন এ দেশে এবং যে কোন দেশে ভোট বিহীন পেশীশক্তি প্রতিনিধি আসবে ততদিন সেই দেশে শান্তির আশা করা নিছক অন্ধকারে ঢিল মারার সামিল। তাই কামারের দোকানে কোরআন পড়ে লাভ নেই। দেশে বর্তমানে আইনের শাসন বলতে কিছুই নেই আছে শুধু শুষন। তাছাড়া দেশ এখন কোন হাল অস্হায় আছে এটা আমরা সবাই জানি। তবে স্বাস্থ্য ও হ্মমতা চিরস্থায়ী নয়। আর এটাই চিরন্তন সত্য। অারোও সত্য যে যেমন কর্ম তেমন ফল তাকে ভোগতে করতেই হবে। শেরেবাংলা এ কে এম ফজলুল হক মাওলানা মোহাম্মদ আবদুল খান ভাশানি শ্রেষ্ঠ বাংগালী জাতীর কান্ডারী শেখ মজিবুর রহমান এবং জিয়াউর রহমান এটা এখন আর তাদের কাহারই দেশ না। দেশ এখন শুধু আর শুধুই জুর যার মুল্লুক তার।।,0,crime
ফাসি চাই জানুআৱ দেৱ তাৱাতাৱি,0,crime
আমাদের সমাজে খুঁজলে একজন ও ভালো মানুষ পাওয়া যাবে না। অথচ এরা কারো দোষ পেলেই তার জীবনটা বিষিয়ে পেলে। এদেশে লক্ষ লক্ষ নারী পুরুষ আছে যাঁরা বিবাহ বহির্ভূত সম্পর্ক করেছে। শুধু মাত্র তাদের ভিডিও নেই বলেই তারা ভালো মানুষ এই দেশের মানুষের ছোটলোকি বুঝা যায় এদের এই রকম নিচ আচরণ দেখে।,0,crime
সরাসরি ভিডিও ফুটেজ থাকতে আবার কিসের তদন্ত,0,crime
একে বাহিরে নিয়ে জুতা পেটা করা দরকার। এরা নাকি আবার অপরাধ দমন করে।,0,crime
ধন্যবাদ মাননীয় প্রধানমন্ত্রী কে অপরাদী কে শাস্তি দিবার জন্য তবে আমার খোব কষ্ট আসছে ছোট একটা বাচ্চা তার মাকে ফাসি দিলে এই বাচ্চাটাকেও ফাসি দেওয়া হয় এইটা একটু কষ্ট লাগলো বাচ্চাটার জন্য,0,crime
নুসরাতকে যে ভাবে পুরিয়ে মেরে ফেলছে সেইভাবে ওদের মারার কোন আইন থাকলে ভালো হতো।নুসরাতকে ওরা বিনা দোষে এইভাবে মারছে।ওদের সবার খুব তাড়াতাড়ি ফাঁসি দেওয়া উচিত।,0,crime
এই জন্য ইসলাম ধর্মে মহিলাদের পর্দা করবার হুকুম করা হয়েছে,0,crime
রিফাত কে যখন নিয়ে যাইতেছিল তখন আপনারা ফলো করছেন মিনি অন্য দিকে তাকায় নিশ্চিত মিন্নি এখানে জড়িত আছে গরম ডিম দিলে সব আপনি আপনি বের হয়ে আসবে,0,crime
ডিসি!,0,crime
বাংলার অনেক । পেলেই বাঁশ মেরে হাসতে থাকে । 😎,0,crime
আমি চাই মিন্নি ফাঁসি চাই ওকে,0,crime
এখানে মিন্নি জড়িত থাকার সাইকোলজিক্যাল প্রমান দুটি পাই এই ভিডিওতে প্রথমে যখন ধরে নিয়ে যায় তখন এমন যে হাসব্যান্ড মিন্নিকে ডিস্টার্ব করে তাই নয়ন কে দিয়ে মেরে নিচ্ছে পুরাতন প্রথম ভিডিও তে হাসব্যান্ড কে মারার পর মিন্নি কে ব্যাগ নেওয়ার সময় মনে হয়েছে সে এটা সাভাবিক ভাবেই নিয়েছে মিন্নিকে নিয়ে ইনভেস্টটিগেশন করা উচিৎ,0,crime
মানুষ তো পাগল না যখন দরা খায় সবাই একথা বলে যখন উনি উনার স্যার কিছু করেননি তাহলে উনি কি কারণে একথা বলতেছেন স্যারের কোন দোষ নেই নিজের কথায় তো নিজেই পেসে গেলেন,0,crime
তোমার কেন জলে যখন নুসরাতের বাবা মা কাঁদছিল তখন কোথায় ছিলে। ফাঁসি খুব জরুরি করা হয় যেন।,0,crime
এ হত্যাকাণ্ডের পিছনে রিফাত এর স্ত্রী সরাসরি পাবে জড়িত,0,crime
হা হা হা,0,crime
এই সব কথা শুনবেন না সবাই কে গ্রেফতার করুন সবাই মিথুক,0,crime
পাগল কাকে বলে কত প্রকার এদের কে দেখলে বোঝা যায় হা হা হা,0,crime
যেমন সরকার তেমন ডিসি 👍👍👍,0,crime
মিন্নি জরিত আছে রাইট।,0,crime
তার হেলে দুলে কথা বলা কি প্রমাণ করে।,0,crime
মিন্নীৱ হাত আছে এখানে বুঝা যায়,0,crime
পা য়ে থাকলে মেয়েটা হাটার সময় লেংড়াতো।,0,crime
মিন্নি কে।গেরফ তারকরা হোক,0,crime
নিজের আপকম ধামাচাপা দেয়ার সুজগ নেই বিচার চাই,0,crime
মুন্নি জরিত,0,crime
মহিলা কথা ঠিক ছিল।,0,crime
ভাই কে না চায় একটু সোঝোখ না নিতে,0,crime
ভাই এটি আমাদের ফরিদপুরের ঘটনা আমি জানি,0,crime
এই ভিডিও দেখার পর রিফাতের খুনের সাথে মিন্নির জড়িত থাকার বিষয়ে আর সন্দেহ নাই এই ভিডিও প্রকাশ করার জন্য আপনাকে অনেক ধন্যবাদ,0,crime
বাংলাদেশের প্রত্যেকটা অফিসের মধ্যে কি রকম করে করে লুচ্চামি চলে মেয়েদের সাথেএইজন্য মেয়েদেরকে চাকরি দেওয়ার জন্য পাগল হয়ে যায়।।। শুধুমাত্র লুচ্চামি করার জন্য।।।,0,crime
ওয়া আলায় কুম সালাম রহমতুল্লাহ বারাকার্ত ওসি থেকে ডিসি ভোট ডাকাতের অবৈদ ডিসি লীগ আওয়ামী লীগ ঘর জামাই রাখবে সরকার যখন অবৈদ লীগ ডিসি ক্যান বেডসিট অফিসে নরপষু ডিসি লীগ ওর ফাঁসি চাই,0,crime
সম্পূর্ণ দোষ এই মেয়েটার মেয়েটাকে প্রক্কাশে বিয়ে দিয়ে দেয়া হোক,0,crime
কিছু বলার নাই,0,crime
কান্না করে লাভ নাই।আবেগ দিয়ে দুনিয়া চলে না।,0,crime
এটির বিচার না হলে।তাহলে বুজে নিব।আইনি শাস্তি শুধু গরিবদের জন্য।প্রভাবশালিদের জন্য নয়।তাই উপযুক্ত বিচার চাই।অপরাধী হলে শাস্তি চাই।,0,crime
হাইরে দেশ হাইরে দেশের রক্ষোখ,0,crime
মিননী আসল খুনি ।এবং মিননির সেক্স ভিডিও দেখলাম,0,crime
জে ক্যামেরা টা লাগাই চে তাকে মন তেকে বালো বিচার হবে আসা করি,0,crime
নাজমুলের অভিনয়টা ভালো হয়েছে তবে জারি গানের কথায় কিছু জায়গায় ভুল আছে,0,crime
এরা সবাই টাকা পেতো এখন হয়তো এরা পাই না তাই অভিজান,0,crime
আসসালামু আলাইকুম এই সম্পূর্ণই পরিকল্পনা মুন্নির,0,crime
আমি মনে করি যে ওকে খুন করছে তার বউ,0,crime
এর পর জারা অমন অপরাধ করবে তারা দেখো আর ভেবে দেখো এসব করে কে কি পেলাম,0,crime
সালার ভন্ড শিক্ষক মিথ্যা কথা বলছে বলেছিল বৃস্টির বিদ্যুৎ চমকানিতে সি সি ক্যামেরা নস্ট এর ও বিচার হওয়া উচিৎ,0,crime
মিন্নির ফাসি চাই,0,crime
আমি মনে করি এই হত্যার পিছনে মিম্নি অবশ্যই জড়িত কারণ রিপাত কে যখন মারতে মারতে নিয়ে যাচ্ছিল কলেজ গেইট এর সামনে থেকে তখন মিন্নি সাবাবিক ভাবে পিছনে পিছনে হাঁটছে তখন কেন মিন্নি স্বামীকে বাচানোর জন্য এগিয়ে আসিনি,0,crime
ডি সি সাহেব কি বাচ্ছা।আপনি যে নোংরা সাংবাদিক আমরা বুঝতে পারছি।আপনি ডি সির দালাল।মেয়েরা যদি রাজি থাকে তাই কি এইরকম অপকর্ম করতে পারে।আপনি কি আপনার মায়ের বোনের রাজির মাধ্যেমে এইরকম কুকাজ করে আপনি কি আপনার মা বোনকে মেনে নিবেন।নোংরা সাংবাদিক কোথাকার।যেনার করার বিচার করা উচিৎ।যেনার বিচার মৃত্তুদন্ড হওয়ার দরকার।,0,crime
আমার একটাই দাবি মেটির ফাসি চাই কেনো না ওকে দেখে অন্নো মেয়ে রা এমন জানোয়ারের পরিচয়ে দিতে পারে আর জেই পসু গুলো এমন বাবে কুপিয়েছে ওদের কেউ ফাসি চাই ফাসি ফাসি চাই,0,crime
অন্যায় করার সময় মনে ছিল না নুসরাত যখন কেঁদে ছিল তখন তোদের দয়া হয় নাই আল্লাহর দয়া ও হবে না তোদের মতো পাপীর কি ভাবে ছিলি তোরা ধরা পরবিনা খুব শক্তিসালি তোরা এবার দেখ আল্লাহর বিচার।,0,crime
এর লজ্জা নাই,0,crime
এখন এসব এর বিচার হই না,0,crime
কোন বালও হবেনা দশ পনের দিন সব ভুলে যাবে এই রকম অনেক ইতিহাস দেখেছি কিছু দিন পর আবার অন্য কিছু ভাইরাল হবে তখন সবাই ওটা পিছনে ছুটবে আর বাংলাদেশের আইন গরিবের উপর কাজকর হয় বড়ো লোকের জন্য নই,0,crime
সরকার কিছু দেখেনা বিচার করেনা,0,crime
মিন্নি এত ঢং করে কথা বলছে কেমন করে,0,crime
আইনের আওতায় আনা উচিত,0,crime
ছোট মানুষ তাই একটু কম বুঝি তবে বুঝতে পারতাম রাজিব যখন শাবানার আচল ধরে টানাটানি করতো তাহলে পরের শিন কি হবে? প্রথমআলো প্রকাশিত একটা ভিডিও দেখেছি ওটাতে পরিষ্কার বুঝতে পারছি স্ত্রি নাকি ব্যাশ্য? মাপ করবেন যদি কারো কাছে খারাপ লেগে থাকে,0,crime
এমন মানুষ দুনিয়ায় কি মানুষ আছে ভাবতে কস্ট হচ্ছে,0,crime
বেশী করে বার বার সকল মিডিয়ায় প্রচার করবেন।,0,crime
আমাদের সম্মানিত মেজিস্টেট ভাই আপনাকে অসংখ্য ধন্যবাদ জানাই তবে আপনাকে সতর্ক অবস্থান এবং শক্ত হাতে অবিজান চালাইতে হবে আপনি কাউকে পরওয়া করবেন না আপনার সাথে আছে র‍্যাববাহিনী এবং জনগণ।,0,crime
এই সরকারইতু ইসলাম বিরুদি ডিসির দারি থাকলে বলতু আলেমরা এমনি এই আওয়ামিলীগরা শুধু আলেমদের বিরুদ্ধে,0,crime
দারুণ একটা কথা যে দাড়ি ছিলো না আজ যদি হতো কোন মাওলানা তাহলে সারা দেশের মানুষ নেমে যেতো ঠিক বলেছেন আপনি,0,crime
ওর চোখে মুখে ইস্পস্ট বুজা যাচ্ছে যে প্রাকৃত পক্ষে ওএই অপরাধি,0,crime
কোন কিছুই গোপন নেই। মানুষ সব দেখছে তুই জাহান্নামে যাবি মিথ্যা বলে পার পাবি না,0,crime
এসব নাটক আর দেখতে বালোলাগেনা তারা তারি জুলায়া দেয়,0,crime
এয় কলেজের সবাই হিজলা আল্লহ তুমি বিচার করো আমিন,0,crime
তোদের আর কোন কাম নাই নাকি,0,crime
তিনি সত্য কথা বলতেছেন তার কি প্রমাণ তার রুম তার কর্মি একেই বলে সরকারি কার্মকর্তা,0,crime
মিন্নির ফাসি চাই শাতে জারা আছে তাদের সবার ফাসি চাই। বাংলার জনগোন।,0,crime
এই হলো আমাদের দেশের অবস্থা,0,crime
আমি চাই ওদের কেউ পুরিয়ে মারা হক,0,crime
যে সময় নসরাত কে সবে মিলে মেরেছিল। তখন ওরা খুশী ছিল।,0,crime
ভাই আপনাকে ধন্যবাদ সত্যি গঠনা জন্য দেখতে মন চাই,0,crime
লীগ করলে আর কি তদন্ত হবে। এমনই চলছে আজ কাল। দেশ। বিনা ভোটের আমলারা আর কেমন হবে।,0,crime
এই কান্না দেখেও ঠোটের কোণে হাসি আসে,0,crime
দিনের রিমান্ডে দে না,0,crime
প্রকাশ্যে চুমু খাওয়া এই দেশে অপরাধ ঘুষ খাওয়া কখন ই নয়।,0,crime
এটি যদি সত্য না হতো তাহলে এত এডিট করা যেতনা সে এই কাজটি করছে বিধায় তাকে দেখানো হয়ছে,0,crime
এখানে মিন্নি ও জড়িত। ওর স্বামীকে ধরে নিয়ে যাচ্ছে আর ও কত সুন্দর করে পিছন পিছন হাটছে।,0,crime
যাই হোক মেয়েটা সব খুলতে পারলো কিন্ত চুল ঢেকে রেখে দিছে😂,0,crime
তিন ইঞ্চি নদীতে সাড়ে তিনহাত দুইটা নৌকা ডুবে গেল।। এই নদী বেঁচে থাকলে আরও নৌকা ডুববে।,0,crime
ফালতু বিডিও রিফাতের কাহিনীর সাথে বনে নাই,0,crime
এখন মিননী কে ও রিফা ফরাজী ও রিশান ফরাজী ও অন্যাখুনীদের কে ফাঁসি দেওয়া উচিত ।খুব দূরত ভাবে।,0,crime
আপনার কে ধন্যবাদ।,0,crime
শাস্তি দেবে এ কথা বিশ্বাস করতে পারছি না,0,crime
যাওয়ার সময় সব এটাক ইন্জিনিয়ার😀😀,0,crime
ছিছি দেশটার কি হালঅবসথা একজন অত মাবুদ রহম কর আমাদের,0,crime
ভাই আপনারা দেখবেন।স্থানীয় আওয়ামীলীগ বা কেন্দ্রীয় পর্যায় থেকে বলবে।এটি ও গুজব। আওয়ামীলীগ এই লোকের বিরুদ্ধে কোন কিছুই করবে না।কারণ রাতে ঐ রুমের মত জায়গায় ভোট চুরি করিয়েছিল আওয়ামীলীগ আর তারা এখন ক্ষমতায়।কাজেই যাদের দিয়ে ভোট চুরি করিয়েছিল আজ তারা এটুকু আমদ ফুর্টি তো করবে আপন লালসা মিটাবে।,0,crime
সব ই বুঝলাম । কিন্তু যেখানে পিস নিয়া ধরা খাইলেও কয়েক বছর জেলে থাকতে হয় সেখানে ইয়াবা নিয়ে ধরা পড়া আসামী ছাড়া পায় কিভাবে,0,crime
অনেকদিন সেক্স না করতে পারায় অসুস্থ হয়ে পড়েছে,0,crime
এটা বাস্তব ঘটনা,0,crime
উচিত শিক্ষা আরেক যন বলে আল্লাহ বিচার করবো।,0,crime
উচ্চ আদালত কি ওদের ফাসির রায় বহাল রেখেছে??,0,crime
সুজন কাকার মতো সবাই ভাত খাইতে ক্লাবে যায় 😆😆😆,0,crime
আমার খুব দুঃখ হয়,0,crime
দুজনের ইচ্ছার পক্ষে তাই এএটা নিয়ে মাথা ঘামানোর কিছু নাই।,0,crime
আর কে বাকি আছে।,0,crime
জুয়া খেলায় প্রশাসন জড়িত আছে নাইলে জুয়া খেলা এমন ভাবে চলতে পারেনা দিনের পর দিন,0,crime
এই মেয়েটাকে রিমান্ডে নিয়ে গন ধোলাই দিলে সব সত্তি বেরিয়ে আসবে,0,crime
চুরি সবাই করে বাট ধরা খায়না সবাই😃 এই লোকটার ব্যাড লাক🤣,0,crime
প্রশাসকের এই দোসা,0,crime
এরকম আর্তনাত আর হাহাকার নুসরাতের পরিবারের প্রত্যেকটি মানুষের হৃদয়ে কম্পন সৃষ্টি হয়েছিল। তখন কোথায় ছিলো তোমার বিবেক।,0,crime
একটা মেয়ে এতগুলি সন্রাসীদের সাথে কিছু কি করতে পারে?,0,crime
ভেড়ায় ক্ষেত খায়।,0,crime
কিছু করার নেই আওয়ামীলীগের দেশ এইটা কিন্তু তর আর তর স্যারের বাসর ঘর খুব সুন্দর আছে,0,crime
আবুল হোসেন,0,crime
যিনাকারীর বাঁচার কোন উপায় নাই পাথর মারা হোক দুজনের উপর প্রথমে মেয়ের বাবা এবং ছেলের বাবা মারবে পরে বাচ্চা কাচ্চারা মারবে,0,crime
চোর দিয়ে কখনও চোরের তদন্ত হয়না দেশের প্রতেকটি ঘটনা যে ঘটায় সেই তাঁদের লোক দিয়েই তদন্ত কমিটি ঘটন করা হয় তাহলে দেশের সাধারণ নাগরিকরা কি ভাবে সত্য জানবে বুঝবে দুর্নীতি জিনা গুম খুন বেবিচার এই দেশ এমন একটা জঘন্যতম স্হানে পৌঁছেছে যাঁর আজকে টাকা ক্ষমতা আছে তাঁরাই সব কিছু আর সাধারণ জনগণ হলো কচু,0,crime
হায়রে বাংলাদেশ,0,crime
খানকি,0,crime
ভাই এই নারীকে পুলিশে দেন সব কাথা বের হবে,0,crime
গ্রেফতার করে জেলে বসে বসে খাবে তা হবেনা যারা রিফাত হত্যার সাথে জড়িত আমরা তাদের সবার ফাঁসি চাই,0,crime
ওসি মুয়াজ্জেন ফাসি ছাই সে জদি মামলা সুরুতে নিতো তাহলে এমন হতো না,0,crime
সব দোষ যে গোপনে সি সি টিভি লাইছে এই মহিলা চাইছে তার বিচার হোক। ডিসি আর আমার কোনও দোষ নাই। ডিসি জামালপুইরা দিছি ভোইরা ঘড়ে থাকতে বউ মজা নিছি ফাউ,0,crime
বোকা চ,0,crime
কাহিনী হয়নায় সালা আবুল তাবুল,0,crime
সন্দেহ থেকে যাই। ছেলেটা আহত অবস্থায় মেয়েকে নিয়ে সে একাই চলে যাচ্ছে। কেন? মেয়েটা ব্যাগ নিয়ে দাড়িয়ে। কিন্তু কোন অস্থিরতা নেই। যা স্বাভাবি ঘটনা বলেই তার কাছে মনে হলো। অথচ সে মারা গেলো। কি জগন্য কি নিষ্ঠুরতা। আরো তদন্ত করা হোক।,0,crime
সব কিছু নিয়ে বাড়াবাড়ি করা উচিত নয়,0,crime
হা হা হা হা হা কি মজা কি মজা মজা পাইলাম ভাই,0,crime
অপরাধী র ফাসি চাই।।তবে পরিবার যে কান্নাকাটি করছে তা স্বাভাবিক কেও চায়না যতই খারাপ হোক আপন কে হারাতে।,0,crime
এতগুলো মানুষের সামনে এই নির্মম হত্যাকাণ্ড হলো। কেউ এগিয়ে আসার প্রয়োজন বোধ করেনি।একসাথে টা মানুষ ও যদি গুন্ডাগুলোকে দৌড়ানি দিত এই হত্যাকান্ড ঘটত না।,0,crime
সব গুলোর ফাশি চাই,0,crime
যে আপলোড দিছে তাকে অনেক অনেক ধন্যবাদ সরকারি উচ্চ পরযায়ের কর্মচারী ওফিসে বসে বসে কত ভালো কাজ করে এখন মানুষ দেখতে পারলো।,0,crime
বাংলাদেশ কি কোন আইন নাই ভিডিও তো তো পুরা পোস্টে বোঝা যাইতেছে যে মিনি জড়িত একবার বের হয়েও মিনি ওই দিকে তাকায় ওরা কোথায় তখন যদি মিনি বাইকে উইঠা চইলা যাইতো তাহলে হয়তোবা এটা হতো না বাংলাদেশের আইন কি এতই ঢিলা ঢালা বোঝেনা এখনই মিনি কে গ্রেফতার করে রিমান্ডে নেওয়া উচিত এই শালী মেন খুনি,0,crime
বুইড়া খাঁঠাস,0,crime
কয় কি এটা হাস্যকর বিচার চায়,0,crime
এক টা কাজ করার সময় হুস থাকেনা,0,crime
আমি ও মেয়েটির ফাঁসি চাই কান্না ধরে রাখতে পারিনি,0,crime
মনির সন্তানটির ডি এন এন টেস্ট করানো দরকার আমার মনে হয় সন্তানটি সিরাজুদ দোল্লার আপনারা কি মনে করেন ?,0,crime
দেখুন আপনি যে কাজ করছেন এরপরে আপনি আবার বেঁচে থাকতে চান এরকম নিকৃষ্ট কাজ মানুষের সামনে প্রকাশ হওয়ার পর বাঁচতে মন চায় কিভাবে আপনার এতটাই খারাপ এতটাই নির্লজ্জ হয়ে গেছেন আপনি যার জন্য দেহ ব্যবসায় নামছে,0,crime
ওসি মোয়াজ্জেম কে কি ফাসি দেয়া হইবে না?,0,crime
রিফাতের স্ত্রী মিন্নি জড়িত এতে কোন সন্ধে নেই। মিন্নিকে রিমান্ডে নিলেই সব কিছু পরিস্কার হবে।,0,crime
অতি শিগগিরি ফাসি দেখতে চায় জনগণ,0,crime
আমরা সঠিক বিচার চাই,0,crime
মজা তুমিও পাইছো আমিও পাইছি। তাতে লজ্জা থাকার কিছুই না। হয়তো তুমি জোর করে খুলতে তাই আমি নিজেই আগে খুলে দিলাম।,0,crime
যদি এই মিন্নি কে ফাঁসি না দেওয়া হয় তাহলে আবার আমরা শুনতে পাবো এই মিন্নি কোন না কোন রিফাত নয়নের খেলায় মেতে উঠেছে সুতরাং ওকে ফাঁসি দিতে হবে,0,crime
উন্নয়ন বাতাস লাগলে,0,crime
এই সব করে তো এখন আপনাদের লাভ কারণ রিফাত কে হত্যা করে নয়ন হীর হল আর পুলিশ থাকে কুকুরের মত মারলও আর আপনেরা নাটক করেছে তার মানে আপনারা এখন টাকা জোগাবার পথ পেয়ে গেছে এর আগে এই সব নাটক গেলে কয়ই,0,crime
এটা মুছে দেওয়ার জন্য অনুরোধ করছি ।,0,crime
এরা সব পান্ডা।এদের কঠিন শাস্তি হওয়া জরুরী।,0,crime
এক রূপবতী মেয়ে সুন্দরী প্রতিযোগিতায় অংশ নিয়ে রূপের চমক দেখিয়ে সবাইকে পেছনে ফেলে প্রথম হয়ে গেল সে! সেই সুবাধে মিডিয়ায় ছড়িয়ে পড়লো তার সুনাম! মেয়েটা যে সুন্দর ছিলো সে ব্যাপারে করো কোনো সন্দেহ নেই। সোশাল মিডিয়া তার ছবি বাইরাল হয়ে চলছে কত রুপ কত সুন্দর চুল নাক চোখ মুখমন্ডল দেহ নিয়ে উনি খুবই অহংকার করে আমি বিশ্বের সেরা সুন্দর মেয়ে অথবা ছেলে এবং মানুষ কয়েকটা নাটক সিনেমায় অভিনয়ও করে ফেললো! অবশ্য অভিনয়ে চান্স পাওয়ার জন্য তার সুন্দর শরীরটাকে কয়েকটা পশুর ভোগবস্তু বানাতে হল। কিন্তু তবুও সে হ্যাপি! তার বিশ্বাস এই শরীরটা কিছুদিনের মধ্যেই তাকে বিখ্যাত করে তুলবে! কিন্তু তার কপাল খারাপ! সেদিন রাতে বাসায় ফেরার পথে আত্মীয় হাতে খুন হলো সে! বাবা মা ও আত্নীয় স্বজনদের চোখের পানি ঝরিয়ে মাটির নিচে জায়গা হলো তার। তিনদিন পর তদন্তের স্বার্থে তার লাশটা কবর থেকে উঠানো হল। কিন্তু একি! তার লাশটা উঠানোর পর উপস্থিত কয়েকজন বমি করে দিলো! এমনকি তার জন্মদাতা মা বাবাও লাশের দুর্গন্ধে নাকে রুমাল চাপা দিলো! যে আবেদনময়ী শরীরটা দেখার জন্য হাজার হাজার চোখ পলকহীন চেয়ে থাকতো সেই শরীরটার একি অবস্থা! অথচ এই শরীরটার জন্যই সে বিখ্যাত হওয়ার স্বপ্ন দেখতো! তাই বুঝি তার বিখ্যাত শরীরটা সবাইকে দুর্গন্ধ বিলিয়ে শেষ বিদায় জানালো! প্রিয় আপু ভাইয়ারা এই সুন্দরী সুন্দর রুপবতী শরিরটা আল্লাহর দেয়া নেয়ামত তাই তোমাকে তার হুকুম মানতে হবে আল্লাহ ইচ্ছা করলে তোমাকে আমাকে ল্যাংরা অন্ধ কানা বানিয়ে এই দুনিয়াতে পাঠাইতে পারতেন কিন্তু তিনি তা না করে আমাদের কত কিছুই না দিয়েছেন কত সুন্দর করে সৃষ্টি করেছেন আমাদের কে আমাদের মহান সৃষ্টিকর্তা সর্বশক্তিমান আল্লাহ । আমাদের সৃষ্টির সেরা মর্যাদা দিয়েছন। আসুন আমরা এই নেয়ামতের শুকরিয়া আদায় করি।………,0,crime
মিন্নী কে যদি রিমান্ডে নেওয়া হয় তাহলে সব ধরনের তথ্য বেরহয়ে আসবে,0,crime
খারাপ কাজ সবাই করে যারটা সামনে আসে সবাই তাকে ছিছি দেয় মানুষের খেয়েদেয়ে কোনো কাজ নাই কে কি করলো তা নিয়ে বসে থাকে,0,crime
আমি বুঝি না ডিসি তো এমন কিছু করে নাই যাতে আমার সমস্যা বা রাষ্ট্রের ক্ষতি তাহলে ডিসি কার বাল ফালাইলো তাতে পাবলিকের এত সমস্যা কেন ডিসি একটা মহিলার সাথে ঘুমায় না দশটা মহিলার সাথে ঘুমায় তার ব্যাপার মানছি ডিসি বিবাহিত হয়ে এটা ঠিক করে নি এখন এটা তার ফ্যামিলি বন্ধুবান্ধবরা বুঝাবে পাবলিকের মাথা ব্যাথা কেন লম্বা লম্বা কথা অনেকেই বলে কিন্তু সারাদিন ডিসি যা করছে সেই সুযোগের আশায় থাকো আর রাইতে তো পর্ন ছাড়া ঘুমই হয় তারাই কয় ডিসি বালা না।,0,crime
আসলে নুসরাত টা কে? থাকে নিয়ে এতো কথা বলতেছে? দৈনিক হাজারো নুসরাত গ্রাম গন্জে মরতেছে তাদের খবর নিচ্ছ তুমরা? আসলে এই টা মিডিয়ায় উঠেছেতো তাই একটু তুল পার হচ্ছে আর কিছু না।,0,crime
মানুষের রক্ত পানি করা পয়সায় এরা মৌজ মাস্তি করে। যে চেয়ারে বসে জনগণের জান মালের নিরাপত্তার কথা চিন্তা করবে অথচ সেই চেয়ারে বসে এদের মত ব্যক্তিরা জনগণকেই বাঁশ দেয়। এরাই হল সোনার বাংলার সোনার মানুষ।,0,crime
ধন্যবাদ ভাই আপনাকে।,0,crime
স্যার এবং ম্যাডামের কোন দোষ নেই সব দোষ যে ভিডিও করছে তার তাকে বিচারের আওতায় এনে কঠোর সাজা দেওয়া হোক কেন এই ভিডিও করলো আমার কথা না এটা হল এই ভদ্রমহিলার কথা🤪🤪😜😜,0,crime
রিফাতের স্ত্রী মিন্নির হাটা দেখে তহ মনে হয় ও শুধু জড়িত ওর স্বামীকে ধরে নিয়ে যাচ্ছে অতছ ওর কিনো প্রতিক্রিয়া নাই,0,crime
প্রথম আলোর সাংবাদিক ভাইয়েরা ভয় পেও না।সব কিছু ইনভেস্টিগেশন করে যেটা সত্য প্রমান হয় সেটায় রিপোর্ট দিও।অন্য রিপোর্টার দের মত মানুষের আস্থা হারিও না।,0,crime
আর তদন্ত করে কি লাভ হেতেরে ডি এন এ টেস্ট করলেই হইয়া জাইবো সব,0,crime
এটাই বাংলাদেশ।এত মানুষ থাকতেউ কেও বাধা দিল না।কেও সাহায্য করল না।,0,crime
মিন্নী কে রিমান্ডে চাই,0,crime
ওনার বউকে দেখলে মনে হয় ওনার মেয়ের বয়সি এমন বউ রেখে ওনি গেলেন আর্য়ুবেদিক ঔষধ সাধনার কাছে।কুকুর গুলোর বউরা অনেক সুন্দরী হয় তারপরেও ওদের নজর থাকে ডাস্টবিনের দিকে।বাড়িতে বিরিয়ানী রেখে বাইরে ডাল ভাত খেতে গিয়েছিল অনেক সুন্দর গেয়েছেন কেন যে ধরা খেলেন স্যার তে জন পুরুষের চরিত্র আপনার মতো কিন্তুু ধরা খায়না বলে বেচে যায়। সমাজে তারাই বিচার করে।ঘরে কারিনা রেখে।।।।ডিসি গেলো জরিনার কাছে।ছি হায়রে দুনিয়া ইমাম মাহদির অপেক্ষায়,0,crime
তোরে দেখছি তুই মারা দিছিস মুখুস খুল,0,crime
ইসলামিক আইনের বিবাহ করার মানুষ জোদি জিন্না করে যাহয় তা বিচার হক,0,crime
ভাই আমার হুস থাকে না আমি ঘুমে থাকি,0,crime
দুই হাজার আডারো🙄 দেহা করেন। এসব কি,0,crime
বালো মানুষ ছেড়ে দিন খারাপ দের ফাসি হক,0,crime
আমার মনে হয় আগে বলেরেখেছিল যে কয়েকটা কিল ঘুষি দিয়ে চলে যাবেন।কিন্তু পরে মুন্নি দেখে যে রাম দাঁ দি কোঁপানো তারপর সে ঠেকাতে গেছে।ঘটনাটা আমার মনে হয় এমনই হবে।,0,crime
এটা কোন ধরনের তদন্ত যে অপরাধ করে আবার সেই ্্্্্,0,crime
মেয়েটিকে রিমান্ডে নিয়ে জিজ্ঞাসাবাদ করা হোক! তাইলে ওর অভিনয় বের হয়ে আসবে।।,0,crime
সবচেয়ে বেশি খারাপ লাগলো এতগুলো মানুষের সামনে আরেকটা মানুষকে কুপাইতেছে কিন্ত একজন বাদে সবাই সিনেমা দেখতেছে। হায়রে মানুষ! আবার এইখানে অধিকাংশ ছেলে বোধহয় কলেজ স্টুডেন্ট।,0,crime
এতো মানুষে সামনে একটা লোক কে কুপালো কেও কিছুও বলছেনা এই আমরা বাংলাদেশে বাশ করি হাইরে জিবন,0,crime
এক যন ডিসি এই রকম ওনার বৌ কেমব হবে,0,crime
ঠিক বলেছেন,0,crime
যেই যাই বলে সব পিছিয়ে পেলে আপনি এগিয়ে যান,0,crime
চিন্তা করি সন্তানগুলা সমাজে কিভাবে মুখ দেখাবে 😥,0,crime
এদের কে ও আগুনে পুরিয়া মারা উচিত,0,crime
মিন্নি তাদের সাথে জড়িত।।যখন রিফাতকে দরে নিয়ে যাচ্ছিলো তখন রিফাতকে তাদের হাত থেকে বাচাতে মিন্নির কোন ভুমিকায় ছিলো না।।একজন সাধারন পথচারীর মত হেটে যাচ্ছিলো মিন্নি,0,crime
বাংলাদেশে আইন ঠিক হতে হবে তার পড়ে মানুষ শান্তি হবে তার আগে না,0,crime
ভাই সবুজ সাট পরা ওই লোকটি কে? জার কথায় সবাই চলেগেলো? ভিডিও টি ভালোকরে লক্ষ্য করুন।,0,crime
আমার মনে হচ্ছে এই মহিলা খুব বড় মাপের অভিনেত্রী,0,crime
তারপরও বলে স্যারের কোন দোষ নেই। আমি এগুলোর কিছুই জানিনা আপনারা তদন্ত করুন বিচার করুন মেয়ে মানুষ বলে কথা,0,crime
বে আইনি অস্র অদের হাতে বাংলাদেশের পুলিশ👮 কি করে??,0,crime
আল্লাহ তুমি আমাদের কে অন্যায় কাজ থেকে বিরত রাখ। খবর টি শেয়ার করার জন্য ধন্যবাদ,0,crime
সর্ব সর্ব শেষ বললাম এরপর আর মিডিয়া যাওয়া যাবে না তারপর তারা কি করলো তারপর একই তারা সংসদের করে নিল সবকিছু দু তিনদিন শুনবেন সবকিছু তখন সবকিছু সমাধান হয়ে যাবে রাজনীতি কারণে,0,crime
আহারে মানুষ কত রংয়ের ডংয়ের দেখলাম,0,crime
ওদের সবাইকে গুলি করে মারা উচিৎ তাহলে এই রকম হবেনা আর তা নাহলে বন্ধ হবেনা জিবনে।,0,crime
খুনিদের ফাঁসি চাই,0,crime
এত মানুষের সামনে কুপিয়ে মারা হল আর অতচ একটা লোক ও এগিয়ে আসে নাই 😰😰😰সব গুলা কাপুরুষ!!!,0,crime
এতো প্রমাণ থাকতে ফাঁসি দেরি হচ্ছে কেন,0,crime
এক দোম সঠিক কথা ভাই যদি এই মেয়েও তাদের সাথে জড়িত থাকে তাহলে তাকেও তার উপযুক্ত শান্তি জন্য আবেদন করছি যাতে এই থেকে শিক্ষা হয় বাংলাদেশের মেয়েদের,0,crime
বাবারে একি শুনলাম স্যারের কোনও দোষ নাই🤣🤣আজব ভালবাসা😂😂,0,crime
চার মিনিট না মিনিট পুরাটা,0,crime
ডিসি মেছির৷ ফ্রি কিকের গোলটা নিয়েই নিলো,0,crime
দেশটা আগে ছিলো দরিদ্র সীমার নিচে আর এখন চরিত্র সীমার নিচে,0,crime
আমার বিচারে ডিছি চাকরি কে রে নেয়া হোক তার পরে দুজনের বিয়ে দোয়া হোক আপনারা কে কে এক মত আছেন,0,crime
হা হা হা।মনে হয় প্রেগনেন্ট।,0,crime
মেয়ের ই অাসল দোষ,0,crime
ষালা ওই ডিসিকে জুতোর মালা পরিয়ে সবার সামনে ঝাড়ু পিটা করা হোক,0,crime
এবার এসব বন্ধ করেন।,0,crime
ওই মহিলার কি হবে জানাবেন,0,crime
আরেতুয় কাদ কেন নুসরাত এরচেবেসি কাছিল তখন মনত একটুদয়া জাগেনা পাপ কুনুদিন বাবা কেছনা তকে বলছি এরক বোগিনিয়ে বিডিও দিসনান,0,crime
আমি এদের ফাঁসি চাই??? আমার সাথে আর কে কে একমত???,0,crime
জামালপুরের ডিসি সাহেব মধু পান করছেন।ছেলে ভাল আমার মত। আমি ও মাজে মাজে এরকম সাংভিসিং করি। বিদেশে,0,crime
জোরিত,0,crime
যতজন লোক দাড়িয়ে দাড়িয়ে দেখছিল সবাইকে আইনের আওতায় আনা হোক। কার প্রবাদে আছে যে অন্যায় করে যে আর অন্যায় সহে যে সমান অপরাধী।,0,crime
করা আলাদের দোস নেই ক্যামেরাই আলার দোস,0,crime
বিয়ার অনুসটান হর মনেহয়,0,crime
মিন্নি সত্যি পরিকল্পনা করে তার স্বামীকে হত্যা করিয়েছে । ধন্যবাদ,0,crime
হায়রে বাংলাদেশ কি হয়ে গেছে,0,crime
আওয়ামিলীগ সরকার যতদিন থাকবে এই বিচার আর হবে দোয়া করি একজন সত্যনিস্ঠ শাসক আসুক দেশটাতে,0,crime
এর কোনো বিচার হবে না। এখনি এটা আমাদের মতো সাধারণ মানুষ করলে ঠিকই বিচার হইত।,0,crime
এরকম মহিকে মেরেপেলাউচিত,0,crime
মেয়ে ছেলে দুজনই অপরাধ বিচার হবে দুজনেরই,0,crime
আপনার কথা গুলা অনেক ভালো লাগে টিপু ভাই,0,crime
নুরসাত যখন পানি পানি করে কাঁদছে তখন তোরা কোথায় ছিলে,0,crime
আদর করতেও কাপড় খুলতে হয়! 😀😀,0,crime
ওর কথা বলর সময় চেহারার মধ্যেই ফুটে উঠেছে যে এই কাজ করেছে।,0,crime
সেদিন এর থেকে বেশি কেঁদেছিলো নুসরাত। আজ তোমাদের সন্তান বেঁচে আছে কিন্তু নুসরাত এই দুনিয়ায় নেই তার মার কেমন লাগছে,0,crime
কমিটি বাল চিরবে,0,crime
আমার মতে মুন্নি শরীফ এই খুনের সাথে জড়িত আছে কারণ মুন্নি বলছে অস্ত্রের ভয় দেখিয়ে কি যেন একটা সাদা কাগজে সই করিয়ে নিয়েছে নয়ন কেন ও তো একটা শিক্ষিত মেয়ে পড়ালেখা জানে ওকে তো সাধু বলতে পারিনা কোন পড়ালেখা জানা মেয়ে না জেনে কোন সাদা কাগজে সই করবে না আবার অন্যদিকে কাজী সাহেব সাল ওদের বিয়ে হয়েছে এবং কাবিননামা দেখাচ্ছে তাহলে কি আমরা ধরে নিতে পারি না মুন্নির কথা এবং কাজী সাহেবের কথার মাঝখানে কিছু একটা সত্য লুকিয়ে আছে এই সত্য টা পুলিশ প্রশাসনকে অনুরোধ করবো আপনারা ঘেটে দেখুন এইখানে কিছু একটা সত্য পাওয়া যাবে,0,crime
আরে দেখাই তো যাচ্ছে।উনি এইসব করেছে।,0,crime
জোর করে তো করে নাই সমস্যা কি মানুষের এতো চুলকানি কেনো জতো সব বাল,0,crime
আমাদের দেশের মুরুব্বি রা বলে কুত্তার নজর নাকি বিষ্টার দিকে,0,crime
অপরাধি গান শুনতে চায়,0,crime
নুসরাতের চিৎকার কেউ কোনোদিন ভুলবে না ।তাই এদের শাস্তি আমরা দুনিয়াতেই চাই,0,crime
এই ভদ্রলোক নামে নিরলজ্জ তাহলে আগেও আরোও করমিদের সাথে এসব করেছে 😠,0,crime
এতো মানুষ থাকতে একটা মানুষকে মেরে ফেলে দুনিয়াটা আজ কোথায় গেছে,0,crime
আরে ভাই কি বুজে করচেন ওটা কলকাতার একটি ডাক্তার চেম্বারেরে ভিডিও। আমার কাচে লিংক আচে লাগলে বলিয়েন।,0,crime
এটাই আমাদের সোনার বাংলাদেশ 😷😷,0,crime
প্রথমে বিশ্বাস করতে চাইনি তবে এখন বিশ্বাস করি ঘটনাটি তে মিন্নি জড়িত আছে।,0,crime
মেয়েটার করনে আজ দুইটি ছেলের জিবন শেষ,0,crime
মানুষের মুখ হচ্ছে মনের আয়না মিন্নীর মুখ দেখেই বোঝা যাচ্ছে ও মিথ্যা বলছে।,0,crime
এসব কীটদের গুরুত্বপূর্ণ পদে রেখে দেশকে গভীর সংকটে ফেলানোর চেষ্টা হচ্ছে আর কত নিচে নামলে চোখ খুলবে সরকারের।,0,crime
কবে বিচার হবে সারা বিশ্ব যে অপেক্ষা করছে কলিজাটা কবে ঠান্ডা হবে,0,crime
অপরাধীদের কঠিন শাস্তি চাই। যদি প্রশাসন এদের শাস্তি দিতে ব্যর্থ হয় তাহলে দেশে এমন অহরহ ঘটনা দিন ঘটতেই থাকবে,0,crime
আমি চাই সব খুনের বিচার এইভাবে করুক আমাদের দেশে সরকার তাহলে হইতো আরেকটা খুন করতে কেউ সাহস না পায়,0,crime
ভাই বালো হয় নাই,0,crime
কারো অপরাধ কম না কারো জন্য কারো সম্মানের বারোটা বেজে যায় !,0,crime
য‌থেষ্ঠ প্রমান থাকা স‌ত্বে ও আবার তদন্ত কি‌সের যারা তদন্ত কর‌বে তারা ও পর‌কিয়াতে লিপ্ত।,0,crime
আর কিছু থাকলে লাগাও,0,crime
দুনিয়া থেকে জাওয়ার সময় কিছু জাবে না,0,crime
ভাই প্রশাসনের প্রতি আহ্বান জানান যেন মিননি কে গ্রেফতার করা হয়,0,crime
মেয়ের বিচার করা হক,0,crime
এত মানুষের সামনে এক জনকে মারলো সবাই তামাশা দেখলো মানুষ রুপি জানোয়ারের দল অন্তত পুলিশকে ত ফোন করতে পারতো। কোন জগতে বসবাস করি আল্লাহ জানে।,0,crime
মাননীয় স্পিকার আজকাল মিনিটে কিছু হয়না। আমরা পুরো মিনিট দেখতে চাই,0,crime
হবে,0,crime
যুবলীগ আর ছাত্রলীগ মুজিবের প্রতিরূপ,0,crime
যদি সত্যি হয় ডিসিকে বহিষ্কার করে থাকে আইনের আওতায় নিয়ে আদালতে বিচার করতে হবে,0,crime
আর মিন্নি কে রিমান্ডে দিলে বের হইবো যে কে রিফাত কে ফোন দিয়ে বাড়ি থেকে নিয়ে গেছে দোয়া করে এটা বের করুন কে ফোন দিয়ে রিফাত কে কলেজে নিয়ে গেছে,0,crime
যারা করতেছে তাদের কেনো সমস্যা না হলে আমরা তৃতীয় ব্যাক্তি হিসেবে নাক বা গলালাম কারণ বাংলাদেশে হাজারো পতিতালয় আছে যেখানে হাজারে পুরুষ যাচ্ছে তো ওনি যখন ভিয়াইপি ওনি একটু বিয়াইপিটা করবো তো তবে ওনি মুসলমানদের কাতারের মধ্যে পড়ে না কথাটা শুনকে খারাপ হলেও এটা সত্যি সরকারি কমর্কতা এনবের সাথে জরিত কিছু বলার নেই,0,crime
মেয়ে।জরিত।আছে।চলার।মাদ্দমে।বুজা।জায়,0,crime
ভাই বাংলাদেশের নেতা দের চরিত্র ফুলের মতো পবিত্র। তার বাস্বব প্রামান।,0,crime
কথা বুঝায় তু অপরাধি,0,crime
সব গুলো অমানুষ আমি চিনি।।,0,crime
মিন্নিকে ফাসি দেওয়া হোক,0,crime
তোর সন্তান কে দেখানো দরকার এই ভিড়িও,0,crime
এই মেয়ে জড়িত মনে হয়,0,crime
ডিজিটালের নামে দেশ টারে কোন নরকে নিয়া গেসে ছি অাললা কেনো এই বাংলাদেশের বুকে জন্ম দিসিলো ছি ঘিরনা হয় তার চেয়ে জদি কোনো খিরিসটানগ ঘরে জন্ম হইতাম তাহোলে শান্তি ছিলো,0,crime
ওরা বাকি চারজন কুতায়।,0,crime
নুসরাদের খুনির ফাসি যত তারাতারি দেওযা হক এটাই বাংলার নারির বিচার চাই নারি হত্যর বিচার চাই,0,crime
এই সবলোক দের এতো সময় দেয়াজাবে না ওদের কে ধোরে এক হাত ও এক পা ও এক চোক ও কেটেদেয় হোক জাতে আর কোনো মানুস সহস নাপায়,0,crime
হায়রে মুক্তি যোদ্ধা ক্লাব মুক্তি যোদ্ধা ক্লাবে বাংলাদেশের মানুষ কে স্বাধীন করে দিচ্ছে! হায়রে বাংলাদেশ!ধিক্কার জানাই এই সমাজ ব্যবস্থাকে যতো অপকর্মে ই জন্ম দিয়ে থাকে সরকারী চোরেরা!ভাগে কম হলেই অভিযান😄😋,0,crime
আমার খুব আনন্দ হচ্ছে যে খুনীদের ফাঁসির রায় দেওয়া হল । কিন্তু খুনীদের পরিবারের মায়েদের কান্না দেখে আমিও কেঁদে ফেললাম ।,0,crime
এরা জিনা করছে তাদেরকে পাথর মেরে মেরা ফেলা হক,0,crime
দালাল চ্যানেল। সিসি টিভির ফুটেজ দেখান,0,crime
বাস্তব কথা বলছেন।,0,crime
ফাঁসি কেনো ? নুসরাতককে যে ভাবে জালিয়ে মারা হয়েছে ওদেরকে ও ঐ জায়গাতে নিয়ে ঠিক ওভাবেই মারা হোক তাহলে হয়তো আর কোনো নুসরাত মরবে না। অন্য দিকে যথেষ্ট তদন্ত করা হোক যাতে করে যেনো কোনো নির্দোষ লোকের সাজা না হয়।,0,crime
কেমেরা মেনকে হাজারও তালি,0,crime
এটা তো আগের 😁😁😁 আপডেট কি আছে,0,crime
কোন স্বামীকে মারলে বা মারার উদ্দেশ্যে টেনে অন্যস্থানে নিয়ে যাওয়ার সময় কোন স্ত্রী কিভাবে এত ধীরে সু্স্থে সন্ত্রাসীদের পিছনে হাটঁতে পারে??? আমার জানা নেই। স্বামীকে কুপানোর পর স্ত্রী তার জুতা আর ব্যাগ টা আগে খুজে এটা কেমন স্ত্রী??,0,crime
আমার মতে সুন্দরি মেয়ে বিয়ে না করে একটা কালো মেয়েকে বিয়ে করা উচিত কারণ কালো মেয়ে বিয়ে করলে তার দিকে কোন ছেলেরা তাকাবেনা আর সুন্দরি মেয়ে বিয়ে করলে তাকে নিয়ে রাস্তায় বের হলে ছেলেরা সিটি বাজাবে অতএব কালো মেয়ে বিয়ে করা উত্তম আমি মনে করি,0,crime
আমাদের বাংলাদেশে অনেক গরিব লোক আছে একটা গর করার টাকাও নাই টিভিতে সুনটাছি বাংলাদেশে টাকা টুকরা করে নদিতে পেলে দেকুন আমার বারির পাসে ও অনেক গরিব লোক আছে তারা তিন বেলে খেতেও পারে না কেও দোইনিক তিন সো টাকা রোজ কার করে সন সারে তা চলে জাই আর কারো কাছে এতো টাকা টাকার টেন সোনে গুম জেতে পারে না তাদের এতো টাকা তারা টাকা কই থেকে ইনকাম করে টারা নিজেও হিসাব দিতে পারে না ব্যাংককে রাকারও জাইগা নেই তারা সুদু সুদু টাকা গুলা চুরি করে রেকে দেই খেতেও পারে না কিনতু জেই পরি মান টাকা আছে টাকা গুলা জদি সাদা রন মানুষের বিতরে চেরে দেই তা হলে না খাই মরটো না আপনারা দেকুন আমাদের দেশে না খেয়ে মরার গটোনা এহন ও আছে ওননো দেশে কাজ কাম না করেও মানুষ চলা পেরা করতে পারে আর আমাদের দেশে গরিব জারা তাদের গরে এক দিন রোজ কার না করলে কানদা কাটি করতে হই আর সুনলাম বাংলাদেশের মানুষ নাকি টাকা বোসটা বরে নিজের বাসাই রেকে দেই আমি কিনতু সুনে বেজার হইনি আমার কথা গুলা সুনে হাসি আসসে আমার নাম মোঃ রাশেদ আমার বাবা ঢাকা উওর সিটি করপেরেসন এক জন কাওন চিলোর এর কাজ করে বোসোর আর ওনার নাম মোঃ জাকির হোসেন বাবুল ওনার ওচুললাই আমগো সনসারটা বালো বাবে চলে আর জদি ওনার মোটো নেটা জদি বাংলাদেশে পরতেকটা এলাকাই থাকতো তা হলে মানুষের কষট গুলা আর থাকতো না,0,crime
মাইরের উপরে মাইর তার উপর মাইরে দরকার এমন লোকের,0,crime
এটা দেখে বুঝা যায় এটা মেয়েটার জন্য হয়েছে এই মেয়ের জন্য দুইটা জীবন শেষ হয়ে গেছে বাংলাদেশের সরকার কি করে এই মেয়েটাকে এমন ভাবে শাস্তি দেওয়া হোক যাতে সব নারী এই ধরনের কাজ কোনো দিন না করে এটা কি আমার সেই সোনার বাংলাদেশ যে দেশে একটা খারাপ মেয়ের জন্য দুইট জীবন শেষ হয়ে যায় আমার সরকার এর কাছে এটাই চাওয়া মেয়েটাকে শাস্তি দেওয়া হোক,0,crime
বেচারা ক্যামেরায় ধরা খেয়ে ফেসে গেছেন মাইনকার চিপায় !!!,0,crime
আল্লাহ তো বিচার করবেই র্নিঅপরাদ মেয়েটাকে যখন মেরে ফেলছিলো তখন কোথায় ছিলো এত কান্না নুসরাতের মা ও এই রকম করছিলো মেয়েটা মৃত্যু আগে একটু পানিও খেতে পারেনি😓😓,0,crime
এমন বাঙালী ভিডিও করছে তা ও আবার একটু হ বাঙালী,0,crime
মিন্নিকেও আইনের আওতায় নিয়ে আসতে হবে,0,crime
আসলে সবাই দোষ করেনাই কিছু মানুষের ভাগ্য খারাপ থাকে আমরা বুঝি না যখন নিজের উপর দিয়ে যায় তখন বুঝি,0,crime
স্ত্রীকে দেখে মনে হচ্ছে অভিনয় করছে !!!,0,crime
এদের তাড়াতাড়ি উইকেট পালান,0,crime
আমিও খুশি।। মননীয় প্রধামন্ত্রকে অসংখ্য ধন্যবদ।।।এখন আবরার হত্যার আসামীদের ফাসি কামনা করছি প্রধামন্ত্রীর কাছে।।।,0,crime
পাপ কোন দিন বাপকে ছারে নাই,0,crime
হে বনি আদম শয়তানের ধোঁকায় পড়ে দুই চার মিনিটের মজার জন্য তোমার আল্লাকে ভুলে গেলে তোমার দুই চার মিনিটের মজার বিনিময়ে তোমার জন দুই চার হাজার বছরের আজাব গজব অপেক্ষা করতেছে তুমি কি একবার ভেবেছো আজকে তোমার ক্ষমতা আছে পয়সা আছে দুই হাত ভরা শক্তি আছে কালকে সেটা না ও থাকতে পারে তোমার সৃষ্টি কর্তাকে ভয় করো যে আল্লাকে ভয় করবে সে কখনও পাপ করতে পারবে না,0,crime
ক্রোস ফায়ার চালু করা হোক না হলে বেরেই চলবে ক্রোস ফায়ার চালু হলে কিছুটা হলেও বন্ধ হবে,0,crime
আপনি বিচার চান কিন্তু স্যারের কোন দোষ নেই কেন ইহা কমলাকান্তের বোধগম্য নহে। হাস্যকর,0,crime
মিন্নি খুনের সাথে প্রত্যক্ষভাবে জড়িত,0,crime
হে আল্লাহ সবাই কে হেদায়েত করো আমিন।,0,crime
আমাকে এক জন নিয়ে গেছিলো ভাইয়া,0,crime
কিছুদিন আগেই বলেছিলাম এদের কিছুই হবে না কিছু টাকা দিয়ে দিলেই এই চরিত্রহীন বাস্টার্ড রা সব সমাধান হয়ে যাবে।কথা টা কি ঠিক হলো স্বামী সন্তান রেখে কি এগুলা।আবার এরা মিডিয়ার সামনে এসে কথা কিভাবে বলে সব টাকার খেলা চা খাবেন এখন ঢেলে দেই,0,crime
অপৱাধ কৱে নাই কিন্তু পবিত্র অফিসে এগুলো কি,0,crime
কত বড়ো খারাপ মেয়েটা টা প্রকাশ পেলো,0,crime
ভিডিও যে করেছে তারও বিচার করা দরকার,0,crime
ভাই আপনার কথা গুলো অস্থির,0,crime
এগুলাই সমাজের উচ্চপদস্ত কর্মকুত্তা,0,crime
দ্রুত রায় কার্যকর হওয়াটাই এখন সময়ের একমাত্র দাবি। এই শাস্তি ভবিষ্যতে অপরাধীদের জন্য দৃষ্টান্ত হয়ে থাকবে।,0,crime
একদিন নুসরাতের জন্য ও তার পরিবার ও আত্তিও স্বজন এবং সারা বাংগালি কেদে ছিল।আজ বাংগালি কাদবে না। কাদবে শুধু অপরাদিদের পরিবার।আজ সারা বাংলার মানুষ আনন্দিত,0,crime
এক বিনোদনময় দেশ ।আহা আহা😄😄😄😄,0,crime
আপনার মত ম্যাজিষ্ট্যাট প্রতেকেরই হওয়া উচিৎ।,0,crime
সবিই ঠিক আছে কিনতু আপনার বাংলা রেডিং পড়তে আত কষ্ট হয়কেনো,0,crime
সন্তানের দোহাই দিচ্ছেন আপনি 🤔🤔🤔 নিজের সন্তানের দিকে তাকিয়ে এই কাজটা আপনি না করলেও পারতেন 😱😱,0,crime
দোষ করে অন্যের নামে দোষ দিবে এটাই বাংলাদেশ। এখন ব্যারিস্টার সুমন কোই,0,crime
ভাই আগে জানতাম না সামি বিদেশে থাকি বাচ্চা কি বাভে হয় এখন বুজলাম,0,crime
মিন্নি কে শুদু শাস্তি নয় কঠিন শাস্তি দিতে হবে মিন্নি যে গেইমস খেলছে পুরো বাংলাদেশ কে বোকা বানিয়ে পেলছে নতুন বিডিও পকাশ না পেলে তো মিন্নি পার পেয়ে যেতো আমারা মাননীয় সরাষ্ট মন্তি ও পুলিশের কাছে আবেন করচি এই চরিএহিন বেশ্যা লম্পট মেয়ে মিন্নি কে দুর্ত গেরেপতার করে পাশির বেবস্তা করাহক,0,crime
আবার আসিব ফিরে ধানসিঁড়িটির তীরে এই এইসব আর নেই জীবনানন্দ দাশ। এখন আসলে কার কুপে প্রাণ যায় সেটার ঠিক নেই।এই বাংলা এখন আর আগের মত নেই।,0,crime
আইনের পরিবর্তন আনা প্রয়োজন পুলিশ অপরাধীকে সরাসরি গুলি করে মারবে এটাই নেয্য আইন।,0,crime
এক কথায় হত্যাকারীদের ফাসিঁ চাই ৷,0,crime
খুনি ফাসি চাই,0,crime
সব শেখ হাসিনার উন্নায়ন চালিয়ে যা বা বা,0,crime
সব আসামীদের ফাঁসি চাই,0,crime
এত যেন কান্না করতাছেন তাহলে নিজের সন্তানটাকে ভালো রাখতে পারলেন না 😬😬😬😬😬,0,crime
এইগোলা হলো আললাহর বিচার পাপ বাপকে ছারেনা,0,crime
যারা প্রকাশ্যে কিংবা গোপনে যৌন কাজ করে তাদেরকে ধরে ইসলামিক দৃষ্টিতে সবার সামনে ফাঁসি দেওয়া হোক। তাহলেই শাস্তির ভয়ে কেউই এসব ঘৃণ্য কাজ করার সাহস পাবে না‌ এবং ধীরে ধীরে তা শূন্যের কোঠায় নেমে আসবে।,0,crime
অরে মদ খাওয়া তারাতারি,0,crime
নয়ন তার প্রথম সামি মানুষ জখন মারা জায় তখন তাকে খারাপ বলতে নাই 😂😂 নয়ন ও রিফাতের মা দুজন কেই আল্লাহ শান্তি দেক,0,crime
মিন্নির আগে নয়নের সাথে বিয়ে হয়েছিল এটা সম্পূর্ণ প্রমাণিত। সরকারি কাজী এই বিয়ে সম্পন্ন করেন। এই শালীকে রিমান্ডে নেওয়া হোক। এসব খারাপ মেয়ে রা পরকিয়া করে বেরায়। এদের কারণে এমন ঘটনা ঘটেছে।,0,crime
কে বসিয়েছে এটা সেটা পরে আসুক অনৈতিক কাজ করেছে এটাই মুখ্য বিষয় আপনাকে সুযোগ দিলো আপনিও রাজি হয়ে গেলেন সাধনা বলছেন আমার ক্ষতি করিনি প্রথম দিনেই ক্যামেরা লাগানো হয়েছিল অর্থাৎ সাধনা এই ফুটেজে আসবার আগে তখন কিছু করেননি এতই সৎ মানুষ ছিল কি সাধনা আর ডিসি স্যার এর কারো শারীরিক চাহিদা ছিলোনা ক্যামেরা আছে জেনে কাজ করেননি সাধনা ভালো মতো চিন্তা করে লাইভ করবেন এতো বাচ্চাকে গল্প শোনাবার মতো,0,crime
নয়ন বন্ডকে পুলিশ আইনের আওতায় আনলেই মূল পরিকল্পনাকারী বা পরিকল্পনাকারিনী তা বেরিয়ে আসবে।,0,crime
জারা দিসেন তারা ঘুষ দিয়া চাকুরী নিসেন,0,crime
দুষ্ট মি করছে এখানের দুষের কি আছে,0,crime
এই পুলারে ধরে গরম ডিম দিলে সব বের হবে।মেয়ে যদি রিফাতের হত্যা চাইতো তাহলে সাথে থাকার দরকার কি? আর তাকে কোপ দিবে কেন। এটা পাগলেও বুঝে একে পাবার জন্যতো রাস্তই পরিস্কার করল নয়ন,0,crime
মান সমমান খাইছে,0,crime
এইযে তোমার টিকিট কতো আমিও করতে চাই 🤗😋,0,crime
আসসালামু আলাইকুম আমি আছান উল্ল্যা আমি যমুনা টিভির সাতে একটু যোগাযোগ করতে চাই কি ভাবে যোগাযোগ করা যায় দয়া করে কেও ভলতে পারবেন,0,crime
এই সকলকে ফাঁসি দেওয়া হয় জেন,0,crime
আন্তজাতিক প্রতি মাচ ভালো লাগতেছে,0,crime
কি মজারে! বাড়িতে একটা সংসার অফিসে আরেকটা সংসার,0,crime
উনার চেহারা দেখলে বোঝা যাচ্ছে উনি এই অপরাধ করেছেন,0,crime
হ্যাকাররা ভিডিও বানাই ফেলছে! ইহা হাইস্যকর!,0,crime
আগে।সঠিক।তদন।করতে।হবে তার।পর বিচার,0,crime
এইটা ধামাচাপা দেয়ার চেষ্টা চলতেছে,0,crime
বাংলাদেশের প্রতিটি হত্যার এরকম বিচার হলে জনগণ বুঝতে পারবে ন্যায় বিচার প্রতিষ্ঠিত হয়েছে।,0,crime
এই ভিডিওতে অনেক কিছু দেখার সৌভাগ্য হয়েছে যখন ধরে নিয়ে যায় ওনার বৌ তো রিল্যাক্সে ছিল নর্মাল ভাবে হেটে যাচ্ছে,0,crime
মিন্নি শেষে ওই ছেলেগুলোর সাথে কথা বলছিল আমার তো সন্দেহ হচ্ছে ওই মেয়েকে,0,crime
রাষ্ট্র ব্যবস্থার চরম বিকলাঙ্গতা কাকে বলে হাড়ে হাড়ে বুঝতে পারছি,0,crime
নারে ভাই মিন্নির কোনো দোষ নাই ভালো করে দেখলে বুজতে পারবেন,0,crime
আমরা চাই যমুনা টেলিভিশনের কাছে এই ডিসির মূল রহস্য জনক ভিডিওটি দেখে কিছু তথ্য বেরিয়ে আসে সরকারি চাকরিতে ওই ধরনের নৈতিকতা আছে কিনা এডিটর থেকে আমরা ওদের কঠিন শাস্তি চাই,0,crime
😭এরা কেমন মানুষ জে একটা বাচছা😭 মেয়ের এভাবে মেরে ফেললো ওর 😭একটুও মাইয়া লাগলো না বিয়াদপ😭 😭,0,crime
ভাইয়া চিন্তা কইরো না রিফাত ফরাজি রিমান্ডে আছে রিফাত বল দেবে মিন্নি এমনিতেই দরা খাবে মিন্নিও ছার পাবে না ভাই,0,crime
অবৈধ ভাবে ক্ষমতা য় আসার সকলে গোপন রুমে এভাবেই ভিডিও ছাড়তে থাকুন অবিরাম অন্তহীন,0,crime
আমরা বাংলাদেশী বলেই হয়ত একজন মরে কয়েকজন এর হাতে অনেক জন মিলে উপভোগ করি। শালার একটা লোকের ও কি একটু মায়া লাগলো না কেও কিচ্ছু বলল না করল না।আমরা পোতা ছাড়া জাতি। আর মিন্নির কথা কি কমু সবাই জা বুঝলেন আমিও তাই বুঝতে পারছি।তবে আমি খুব লজ্জিত কারণ আমি বাংলাদেশের পোতা ছাড়া নাগরিক।,0,crime
রুমে ভালো ক্যামেরা লাগানোর জোর দাবি জানাচ্ছি যাছে ভিডিও গুলো স্পষ্ট দেখা যায় আর আমরাও মজা পাই,0,crime
বহিষ্কার করা উচিৎ জলদি।,0,crime
মিনিকে রিমানডে নেওয়া হোক,0,crime
এত মানুষ শুধু দেখল!!!কেও এগিয়ে এলো না???,0,crime
বোধ হয় অন্ত স্বত্বা,0,crime
সমস্যা কি জয় বাংলার কর্মী মুজিবের সৈনিক,0,crime
আল্লাহ আপনি সবাইকে বুজার তুফিক দান করেন ✔আমিন,0,crime
এই মেয়ে টার কারনণে ছেলেটার মূত্য হল,0,crime
সবতো ঠিক বউরে কি জবাব দিবে😚😎😎😎😎😎😎😎,0,crime
মিন্নি সত্যিই অপরাধী ওর প্রাপ্য হলো সাস্তি,0,crime
সব গোলা মানুষ কাপুরুষের মত দারিয়ে দেখলো সব আবালের দল,0,crime
দুমুখো শাপ হচ্ছে রিফাতের স্ত্রী এক সাথে দুইটা ছেলেকে খেয়েছে যদিও একটা ছিল তার মতই বিষাক্ত কিন্তু আরেকটা নির্দোষ ছেলেকেও খেয়েছে আল্লাহর কাছে দোয়া করি পৃথিবীর কোন ছেলের কপালে যেন এই মিন্নির মত বউ না জোটে আল্লাহ এই মানুষ নামের শয়তান থেকে সবাইকে নিরাপদ রাখুক,0,crime
আমরা তারাতারি ফাসি চাই,0,crime
স্যারের দোষ নাই তা তো আমরা নিজ চোখে দেখতেই পারি।,0,crime
জেলা প্রশাসকটাকে আর স্যার বলার মত কিছু নেই।ইয়ার অব দ্যা গ্রেট লুচ্চা বলতে সমস্যা নেই,0,crime
ধন্যবাদ প্রশাসন ভাইদের,0,crime
এখন নাটক হবে আর সাধারণ মানুষ শুধু দেখবো,0,crime
দাবী একটাই খুনীদের ক্রসফায়ার চাই।,0,crime
অনেক খারাপ লাগলো কিন্তু আমাদের কিছুই করার নাই।। একজন মানুষ হয়ে মানুষকে মারছেন এটাও তো খারাপ কথা।।,0,crime
আল্লাহ এ দেশ ও জাতিকে ব্যভিচারী ব্যভিচারনীর কবল থেকে রক্ষা করো।🇧🇩👈,0,crime
এইটা তদন্ত করার কি আছে বুঝলাম না😂😂😂দেশে সব অপরাধ জগতের মানুষের একই কথা তদন্ত চলতেছে চলবেই,0,crime
যখন নুসরাত কে পুড়িয়ে মারছিলো তখন কেমন লেগেছিল নুসরাতের এখন দরদের শেষ নেই দেখছি,0,crime
সর্বনাশি সর্বগ্রাসী লুটে নিচ্ছে দেশটা জনগন চেয়ে আছে দেখবে এরই শেষটা। ডিসি এবার মজা নিলো কোথায় হবে কেসটা বদ্ধ ঘরে শব্দ করে মিটাইলো তার সেক্সটা। দেশবাসী চেয়ে আছে দেখবে এটার শেষটা। অসৎ কাজ করতে করতে বেড়ে গেছে লেজটা অবিচারে ডুবে গেছে আমার সোনার দেশটা। প্রতিবাদের নেই তো ফল বৃথাই শুধু চেষ্টা। ডিসির বিচার দেখবে মানুষ দেখবে সবাই শেষটা। রচনা,0,crime
পরিক্ষায় পাঠাও,0,crime
ষড়যন্ত্রকারীর শিকার হয়েছেন মনে হচ্ছে।,0,crime
বাংলাদেশে বিচার বিভাগ কি হয়ছে উপযুক্ত প্রমাণ থাকার পরে ও। বিচার হয় না কেনো,0,crime
আসসালামু আলাইকুম হে আল্লাহ আপনি দুনিয়াতে এখন ন্যায়বিচার নিজেই তুলুন ওদের আত্মচিৎকার শুনলে হৃদয়টা কেঁপে উঠে জানিনা কে সত্য কে মিথ্যা আপনি জানেন আমার দোয়া আপনার দরবারে কবুল করেন এখন বর্তমান এই দুনিয়াতে ন্যায় বিচার পাচ্ছে না শয়তান চারদিকে ঘিরে আছে তা দেখছি আর পর্দার থেকে দু চোখের জল পড়ছে আর আপনার কাছে দোয়া করছি আপনি সবাইকে হেদায়েত দান করুন আর সঠিক বিচার দেখে কিভাবে আপনার নিরাপদে থাকবেন না যার কেউ থাকেনা তখন তো আপনি নিজেই হেল্প করবেন এখন এই দুনিয়ার কিছু বিচার ব্যবস্থায় দেখিয়ে দেন যা আমাকে দেখিয়ে দিয়েছেন তা অন্য কেউ দেখান,0,crime
লজ্জা ছাড়া মানুষ ছি ছি ছি,0,crime
ঠাকুর ঘরে কে আমি কলা খাইনি।,0,crime
নোসরাতের মাও এভাবে কেঁদেছে নোসরাত ও কেঁদেছে,0,crime
সবাইকে পুড়িয়ে মারিতে হবে।,0,crime
মিনিটের ভিডিওতে দেখা গেছে ডিসি সাহেব শুধু পাস খেলেছে গোলপোস্টে শট করেনি শুধু পাস খেলে মাঠের বাহিরে আউট করেছে গোলপোস্টে শট করতে পারেনি,0,crime
যখন মারছিলো তখন মনে পড়ে নাই ঠিকই আছে বিচার এদের কে ডব্বল দেওয়া হোক,0,crime
তুমি বেচে থাকলা কি জন্য? চোখের সামনে নিজের স্বামীকে কুকুরের মত কুপিয়ে মেরেচে আপসোষ যে তুমি এখনো জীবিত!! আরে আমি হলে তো নিজের স্বামীকে জড়িয়ে ধরে মারা যাইতাম।,0,crime
মনের মদ্দে একটা কস্ট এত গুলা মানুষ দারিয়ে দারিয়ে দেকল সুদু,0,crime
দারুণ দারুণ,0,crime
সব মেয়েটার দোষ ওকে ধরে ইচ্ছে মতো ধুলাই দেওয়া উচিত কি দোষ ছিলো ছেলেটার ভালো লাগছিলো না ডিভোর্স চেয়ে নে মারার কি দরকার ছিলো তিন্নি?তোদের মতো মেয়েদের জন্য ভালো মেয়েদেরকেও কেউ বিশ্বাস করতে চায় না,0,crime
মিন্নি রিফাত ভাইরাল ছিল প্রিয়া সাহা তার জায়গা নিল প্রিয়া সাহাকে ভুলে গেলাে কল্লাকাটার উদ্ভব হলাে কল্লাকাটা থেমে গেলাে ডেঙ্গু মশা জন্ম নিল টি ডেঙ্গু মশার দিন শেষ চা ঢালায় বাংলাদেশ চা । রুমে ছিলাে এসি! আড়ালে ছিল সিসি! আহারে বেচারা ডিসি! । দেশবাসী দিচ্ছে ছিঃ ছিঃ,0,crime
আকাম করছেন আপনি। আবার নিজের আকামের তদন্ত নিজেই করবেন। এখানে ত ভিডিওতে দেখাই যাচ্ছে অপরাধ আপনি করছেন। বাংলাদেশ এর মানুসকে কি আবুলতাবুল বুঝান।,0,crime
রক্ষক যখন বখ্ক একজন উধতম আইন কমকতা চরিত্র অফিসের পাশে ভিআইপি রুম নারীকে অফিসের সহকারী যৌনকমী বেবহার করার জন্য চাকরি দেওয়া মানুষের বিবেক নৈতিকতা মানবতা কোথায় এই অসভ্য বেয়াদব অশিক্ষিত কমকতা কে চাকরি থেকে বরখাস্ত ও পাশাপাশি সর্বোচ্চ শাস্তি দেওয়া হোক আর সকল সরকারের উধতম কমকতা কর্মচারী বুঝতে পারবে অনৈতিক কাজকর্মে ফল কেমন শাস্তি হয় এমন ঘটনা সমাজ দেশ জাতির জন কলংক,0,crime
তাকে অাইনের অাওতায় অানা হোক,0,crime
মেয়েটা কে ফাসি দিতে হবে,0,crime
গু খায় সব মাছে নাম হয় পাংগাস মাছের।😏😏আল্লাহ সবাইকে সহি বুজ দান করুক।,0,crime
ছোট বেলায় শুনতাম ডিসি হতে অনেক সাধনা করতে হয় আর বড় হয়ে বুঝলাম সাধনাকে করতে গেলে ডিসির চেয়ার হারাতে হয় । হায়রে সাধনা তোমাকে নিয়ে ডানেও বিপদ আবার বামেও বিপদ ।,0,crime
আমরা সব গুলি আসামির ফাঁসি চাই।কাবন এরা কোন দিনও ভাল হবেনা। এদের জন্য কোন আফছোছ নাই। যে কয জন আসামি এদের সবাইকে ফাসি দেওযা হউক আমরা এদের ফাঁসি চাই।,0,crime
আওয়ামি অপরাধী,0,crime
ভিডিও দেখেও প্রমান হয়না তাই মংগল গ্রহ থেকে প্রমান আনার কমিটি গঠন হচ্ছে । ভিডিও যিনি প্রকাশ করলো এখন বুঝি তিনিই হবেন প্রধান আসামি ।,0,crime
মিন্নীর হাঁটা চলার ভাব দেখে মনে হচ্ছে জরিত আছে মেয়েটা,0,crime
অাসল অপরাধী মিন্নী। কি বলেন অাপনারা??,0,crime
আহারে সুখ শান্তি😂😂 শান্তনা আর কি😂,0,crime
বিনা কাপড়ে যে আপনার নয়নের ছবি ভাইরাল হয়েছে এইগুলা ও কি এডিট করা বা ভয় দেখিয়ে লিটনের ফ্লাটে নিয়ে গেছে নাকি।। এই মেয়ের সাথে সম্পর্কের কারনেই আজ বন্ধু বন্ধুকে খুন করলো। আর মেয়ে যতোই বলুক না কেন জোর করে এটা সেটা করছে। কাজি অফিসে গিয়ে বিয়ে এবং জন্মদিনের ভিডিও দেখে আর কেক খাওয়া দেখে মনে হয় না আপনাকে কেউ জোর করে এমনটা করছে। তাই আমি মনে করি তদন্ত কর্মকর্তাগন এই মেয়ের বিষয় মাথায় রেখে কাজ চালিয়ে যাওয়া উচিত। আমি এখনো মনে করি এই মেয়ের সাথে সম্পর্কে কারনে হত্যা করছে।।।।,0,crime
নুসরাত তিন ভাইয়ের এক বোন তার জীবন টা কত সুন্দর ছিল তারা তো বাঁচতে দিল না,0,crime
ভন্ড আহসান হাবিব পিয়ারের ভাষ্য ডিসির এগুলো ইডিট করা যায়,0,crime
আসল খুনি মিন্নী,0,crime
হা হা হা ছ্যাড়া দে মা ক্যানদ্যা বাচি,0,crime
ভাইয়া আপনার কথা যে পারসেন রাইট আমি আপনার সাথে একমত আমি মাননীয় প্রধানমন্ত্রীর কাছে আবেদন করি মিনির উপযুক্ত শাস্তি হোক,0,crime
নাটক খুব ভালো লাগলো,0,crime
দুনিয়ার কী অদভূত নিয়ম অপরাধী শাস্তি পেয়ে বেচে যাবে কিন্তু তাদের জন্য কষ্ট পাবে কত মায়ের বুক খালি হবে এরা অপরাধ করার আগে একবার ও কি পরিবারের কথা ভাবতে পারল না,0,crime
মুন্নি জরিত বুঝা যাচ্ছে,0,crime
শত শত মানুষ রুপি কাপুরুষে চেয়ে এক জন বীরই উত্তম একজন মানুষও কি ছিলোনা ওখানে যে বলে উঠতো মাত্র আল্লাহু আকবার এগিয়ে এসো সবাই আর এই ডাকই হয় তো যতেষ্ট ছিলো ছি ছি মানুষ বীরত্ব মানুষের শক্তিতে নয় বরং তার ধমনীতে বিদ্ধমান সবাই মরা গরুর বাঘ ছি ৷অধম কাপুরুষের শত বছরের ছেয়ে বীরের এক দিনের হায়াতই শ্রেয় |,0,crime
ডিসির অফিসেই পতিতালয়,0,crime
হুগা মারা সারা। আমরা কিছু বুঝি না। আমরা কি শুধু দুদু খাই।,0,crime
ডিসির জায়গায় যদি মসজিদ মাদ্রাসার ইমাম শিক্ষক হত এতক্ষনে সুশীল চেতনাশীলদের আওয়াজে থাকা যেত না শালার ডিসি তোর কপালে জুতার বারি।,0,crime
আওমিলীগ এর চরিত্র খুব ভাল। তারা খুব চালাক। তার ভোটেও খুব ভাল চুরি করতে পারে। শালার প্রধানমন্ত্রি শেখ হাসিনা বলিল যে ভোট সুন্দর হয়েছে। আসলে হয়েছে যে সাংবাদিক রা পারলনা ভোট চুরি দেখাতে পারলো না। কারণ জোর জার ভোট তার। বিএনপির পাশের ভয়ে তারা সব আসনে ভোত দিতে দেয়নি আর সিল মেরেছে। এতাই সঠিক কথা। মনে না মানলে সব মানুষকে নির ভয়ে বলতে বলবেন সব কথা পাবেন। চুরি এই জামানায় করুক আল্লাহ তায়লা সব দেখেন। আমি কোন দল করি না। শুধু দেখা কথা বলি। কারণ আওয়ামীলীগ ও বিএনপি কন দলই ভাল না।,0,crime
স্যারে তোমার কোনো খতি কারেনায় এটা জাতি দেখেছে নিজের ইজ্জত বিঞি করে খাওয়া তোমাদের মতো নারীদের বেঁচে থাকা আর না থাকা একসমান চরিত্র হিন মহিলা তুমি তাহা জাতি ভালো করে বুজে গিয়াছে,0,crime
হা হা খেলা করবা তুমরা এটার বিচার হবে না বিচার চাচ্ছো ভিডিও করার ব্যাক্তির 😁😁,0,crime
ডিসি সাহেব খুব স্লো কাজ করছে তাড়াতাড়ি করলে কিছু দেখতে পাইতাম,0,crime
হাইস্যকর 🤣,0,crime
সালি,0,crime
এটাই সততি কাহিনি,0,crime
তর বাঁচার ইচ্ছা নাই আমি বলছি তরে বাঁচবার কথা কইলো কেঠা। তর বাচ্চা আমাকে দিয়া দে। আর তুই মরে যা। তর মত নষ্টা মহিলার কাছে এই বাচ্চা থাকলে এ বাচ্চাকে সারা জীবন মানুষের মুখের খারাপ কথা শুনতে হবে। একদিন দেখবি এই বাচ্চা ও তোর মত নষ্টাকে ছেড়ে চলে যাবে কারন তারও একদিন মান সম্মান ভোধ জন্ম নিবে বুঝলি। যা দুরে গিয়া মর,0,crime
দেশের ভিতর গজব শুরু হইলো,0,crime
আমি একজন ভারতীয় আমি বাংলাদেশের পুলিশের কাজে খুশি নয়ই এই ঘটনা ভারতে ঘটলে মিননিই সহ আরও জারা জড়িত আছে তারা সবাই এখন জেলে চাকি পিসতো,0,crime
ভাই যে এ ক্যামরাটা লাগিয়েছে তাকে জাতির সামনে এনে পুরুষ্কার দেওয়া হোক,0,crime
বাংলাদেশে প্রতিটা পুরুষের টি করে বিয়ে করলে এই রকম প্রব্লেম কিছুটা কমবে।আর যারা খারাপ তারা তো করবেই,0,crime
ভাই আপনি আগে রিডিং পরা মুখস্থ করে পরে নিউজ কইরেন🤪 রিডিং পরতে পারেনা নিউজ করে,0,crime
হায়রে নারী তোমারই পার ভালো ছেলেদের জীবন নিয়ে খেলা করতে।,0,crime
যখন তারা নুসরাতকে হত্যা করেছিল তখন তার কী কষ্ট হয়েছিল 😭 তা এবার খুনিরা ভালোভাবে টের পাবে। একইসাথে সাগর রুনী হত্যা অাবরার হত্যাসহ প্রতিটি খুন ও অপরাধের উপযুক্ত বিচার চাই। 😇,0,crime
মিন্নির চেহারা বলে না সে জরিত,0,crime
খুব তারাতারী ফাসির কাজটা করা হোক সত্যি কথা কি লিখতো জা সত্যি তা তো হলেই আর কি সত্যি বাকী অপরাধীর ফাসি চাই ব্যস,0,crime
ওকে এটা সরকারের ভালো পদক্ষেপ।আমি তাকে নিয়ে বেশি মাতামাতি করবো না।কারণ যা হয়েছে দুজনের সম্মতিতে।এখানে দোষ দেখি না।থানায় ধর্ষণ কিছু না আর এটা।আমরা বিডিও দেখলেই তখন অ্যাকশনে যায়।কি আজব এ দেশ আর কি আজব দেশের মানুষ।,0,crime
মুক্তিযুদ্ধার নামের জুয়া খেলা হয়,0,crime
চীন জাপান কোরিয়া যুক্তরাষ্ট্র ইউরোপ রাশিয়া এসব দেশের মতো বাংলাদেশের আইন যতক্ষণ না কঠোর হবে ততক্ষণ ক্রিমিনালরা এরকম অপরাধ করতেই থাকবে নোয়াখালী থেকে মোঃ মশিউর রহমান।,0,crime
মেয়েদের কে কেন এত প্রশ্ন? ওরা তো জব করে,0,crime
বাংলাদেশের পুলিশ জদিরে আবার শুনি নয়ন বন্ড জিন্দা আছে ত মনে করলি পুলিশের খবর আছে,0,crime
তার মুখ দেখলে বোঝা যায় সে অপরাধী,0,crime
দরখাস্তে যে সাধনার মোবাইল নম্বর দেখা যাচ্ছে এটা তো কেউ খেয়াল 😂😂😂করতেছেন না।,0,crime
আমাদের দেশের মুক্তিযোদ্ধার নাম ডুবিয়ে দিয়েছে এই সমস্ত ক্লাব জুয়া খেলে,0,crime
কমেন্ট পড়ে বুঝলাম বাঙালিকে কমেন্ট এর অস্কার দেওয়া উচিত।,0,crime
ভিডিও টি যে দেখবে সে বলবে যে মিন্নি এর সাথে 💯 জড়িত,0,crime
মজা তুমিও পাইছো আমিও পাইছি ঠিক আছে,0,crime
বাংলার মানুষ আজ সন্তুষ্ট নুসরাত কে আল্লাহ জান্নাত বাসি করুক আমিন,0,crime
উনি ডিসি সরকারী বড় চাকরী করে উনি করতেই পারে।এটা কোন অপরাধ না।,0,crime
হা হা হা সারের কোনো দোষ নাই তোর ও কোনো দোষ নাই তাহলে দোষ টা ক্যামেরার 😂😂😂,0,crime
এসব করে কি হবে। তকন ত কেউ পতিবাদ করে নি।সবাই মিলে পতিবাদ করলে এসব কিছু হত না।,0,crime
রিফাতকে যখন ওরা ধরে নিয়ে যাচ্ছে তখন মিন্নি পিছে পিছে আপন মনে হেঁটে যাচ্ছে।,0,crime
এই ফুটেজে মিনিট কাটা হয়সে কেনো,0,crime
গায়ে কেরুসিন দিয়ে আগুন দেওয়ার কথা কি মনে নাই বোন নুসরাত কিভাবে চিৎকার করছে পানি পানি,0,crime
বেপর্দা সুন্দরী নারী অমঙ্গ।,0,crime
আপনি ঠিক আমার মনে কথা বলছেন,0,crime
সামীকে মারতেচে আর উনি চেগায় চেগায়া পিচনে হাটতেচে,0,crime
আমি মিডিয়া কে বলছি আপনারা মিন্নী কে জিজ্ঞেস করে না কেন জরিতো আছে,0,crime
হাজার সাবস্ক্রাইবারের চ্যানেলে রিডিং পড়ে একজন স্বল্প শিক্ষিত লোক ভাবতেই অবাক লাগছে। রিডিংটা ভাল করে আয়ত্ব করে তারপরে ভিডিও বানানোর অনুরোধ রইলো।,0,crime
পুলিশ বলে কিছু হয়না,0,crime
এই হত্যাকাণ্ডের সাথে জড়িত সবাইকে যাঁর যাঁর অপরাধের স্তরে বিচার করা হোক এবং প্রকৃত হত্যাকারীদের মৃত্যুদণ্ড কার্যকর করা হোক,0,crime
এই মেয়ে খুন করাচে,0,crime
সে তো অনেক কিছু বলবে যে সব নাটক এ পুরো মিনিটের ভিডিও রয়েছে তার সে রে বছরের সাজা করা হোক,0,crime
হুম খুব ভালো হয়েছে তবে সৌদির মত প্রকাশ্যে শাস্তি টা হলে দেশে অপরাধ অনেক কমে যেত,0,crime
সবতো দলীয় লোক কি বিচার হবে আর এদের জন্য সাত খুন মাফ,0,crime
সালাম ভাই চালয়ে যাও।,0,crime
এই সমোচথো কাম কতো যে খারাপ। সংসার তো ভাংবেই। কতো অপমান। মানুষের কতো কথা। কুথায়ও মুখ দেখানোর জায়গা থাকে না।যতো দিন দুনিয়াতে বাচবে এই কলংকো নিয়ে বেচে থাকতে হবে।,0,crime
ও তো ঠিকই বলছে স্যারের কোন দোষ নাই স্যার তো আর ও কে জোর করেনাই তারও তো সম্মতি ছিলো।,0,crime
কোন সন্দেহ নেই এই খুনে মিন্নি অবশ্যই জড়িত। ওকে ধরে রিমান্ডে নিলেই ওর কু কৃত্বি ফাঁস হয়ে যাবে।,0,crime
সিরাজুল দোলার কি রায় হলো।,0,crime
দাই নিবুরি,0,crime
এই ডিসির ভিডিও সোশ্যাল মিডিয়ায় যেই লোকটা ছাড়ছে ওকে নোবেল পুরস্কার দেওয়া হোক আমার সাথে কে কে একমত,0,crime
যখন আকাম কুকাম করেছ তখন নিজের ছেলে মেয়ের কথা মনে ছিলনা বিচানা শয়তান এসে গরম করেছে,0,crime
জনকে আটক করেছে খুব ভালো কথা কিন্তু সাধারণ মানুষকে ছেড়ে দেওয়াই ভালো আর যারা ক্যাসিনো চালায় তাদেরকে জেল দেওয়া ভালো ভালো,0,crime
এই মেয়ের সাথে এখন বিয়ে দেওয়া হউক।,0,crime
এখন না কেঁদে নুসরাতকে পুড়ানোর কথা মনে পড়ে না এভাবেই একদিন নুসরাতের মাও কেঁদে ছিল দ্রুত ফাঁসি কার্যকর করা হোক,0,crime
এদেরকে বেশি করে সাচ্তি দিতে হবে জাতেখে আর কেউ জাতে কেউ না করতে পারে ওকে দেশের ধিতর নস্টামি করছে আর আমাদের দেশের মে গুলো আর কাজ পায় না কত কাজ দেশে আর মেরা বিদেশ জে নস্টামী গারমেন্সে কাজ করে কেন দেশের মে সব দেশে কাজ করুক গারমেন্সে তাহলে দেশের উন্নতি হবে আমার একটা দাবি দেশের প্রধানমন্তী সেখ হাসিনা মেডামকে উদ্দিসো করে বলছি দেশেন মেয়ে গুলোকে বিদেশে না পাঠাতে দেশে কাজ করুক কি বলেন বন্দুরা সবাই এক মত নাকি আমাদের মুসলিম দেশ ইসলামি কিছু রাখছে না মেয়েরা বিদেশ জে নস্টামী করে দেশের বদনাম করে সব,0,crime
প্রধানমন্ত্রীর কাছে ইরাকী প্রবাসীর খুলা চিঠি সম্প্রতি ইরাকে নতুন সরকার গঠিত হওয়ার পর ইরাকে অবস্থানরত প্রবাসীদের কোন রকম নোটিশ ছাড়াই গ্রেফতারসহ নানারকম পুলিশি হয়রানি করা হচ্ছে। প্রবাসীদের এই সংকট দূরীকরণে মাননীয় প্রধানমন্ত্রী শেখ হাসিনার হস্তক্ষেপ চেয়ে খোলা চিঠি লিখেছেন এক প্রবাসীর । পাঠকের সুবিধার জন্য সেই চিঠি হুবহু তুলে ধরা হলো খোলা চিঠিঃ দেশে থাকা হাজার লক্ষ পরিবারের ক্ষুধা নিবারণ করার প্রচেষ্টায় আপনজন ছেড়ে প্রবাস যাপন করাই কি গুরুতর অপরাধ মাননীয় প্রধানমন্ত্রী দেশরত্ন শেখ হাসিনা আপনাকে বলছি আপনিতো এদেশের প্রধান মন্ত্রীই শুধু নন আপনি বঙ্গবন্ধু কন্যা। এদেশের প্রতিটি নাগরিকের প্রধান মন্ত্রী আপনি। দেশরত্ন আপনি দেশ বিদেশের সকল খবরাখবর রাখেন সম্প্রতি সময়ে ইরাক প্রবাসিদের উপরে জুলুম নির্যাতনের বিষয়টিও আপনার নজরে আছে বলে বিশ্বাস করি। ইরাকে লাখো বাঙ্গালির বসবাস যারা বাড়ি ভিটা বিক্রি করে পরিবার পরিজন ছেড়ে পাড়ি দিয়েছেন। দিনরাত পরিশ্রমের আয় থেকেই নিজে এবং পরিবারকে খাবার যোগান দেয়। শুধু তাই নয় প্রবাসিদের পাঠানো অর্থে বিপুল পরিমানে রেমিট্যান্স জমা হয় সরকারি কোষাগারে। যা দেশের উন্নয়নে ব্যায় করা হয়। তাদের জীবন আজ বিপন্ন প্রায়। মাননীয় প্রধানমন্ত্রী সম্প্রতি ইরাকে নতুন সরকার গঠন করে। সরকার গঠনের কয়েকদিনের মাথায় নোটিশ ছাড়াই কিছু নিয়ম চাপিয়ে দেয় প্রবাসিদের উপর। যার জন্য আজ প্রবাসী বাংলাদেশিরা হুমকির মুখে আকামা না থাকার অপরাধ দেখিয়ে হাজার হাজার বাঙ্গালি আজ অন্ধকার কারাগারে। যার মধ্য আমার আত্মীয় স্বজনও রয়েছেন। আরো উল্লেখ্য যে এই অবৈধ্য অভিযানের নামে বৈধ প্রবাসীরাও গ্রেফতার নির্যাতন থেকে রেহাই পাচ্ছেনা। যাকে মধ্যযুগীয় বর্বর নিপীড়ন বলা যেতে পারে। বিগত দীর্ঘ সময় আকামা বন্ধ রেখে নতুন আকামা করার সুযোগ বন্ধ করে রাখেন। সরকার পরিবর্তন হবার পর আকামার সুযোগ না দিয়ে রাতারাতি সবাইকে অবৈধ ঘোষণা করে রাতের আধারে কারাবন্দী করছেন। এই পদ্ধতি পুরাতন বা বর্তমান অবস্থানরত প্রবাসিদের বিতাড়িত করে নতুন করে ফায়দা লোটার একটা ষড়যন্ত্র বলে আমার মনে হচ্ছে।   সুতরাং দেশরত্ন মাননীয় প্রধানমন্ত্রী আপনি ছাড়া এই সংকটময় ইরাকী বাংলাদেশীদের জুলুম নির্যাতন নিপিড়ন থেকে রক্ষা করার কোন অভিভাবক নেই। আমরা ইরাক প্রবাসি পরিবারের পক্ষ থেকে সবিনয় অনুরোধ করছি আপনি বা আপনার আওয়ামী লীগ সরকারের হস্তক্ষেপ কামনা করছি। আমাদের বাবা স্বামী ভাইকে নিরাপদে কাজের পরিবেশ সৃষ্টি করে দিয়ে আমাদের জীবনমান সংসার ও পরিজনকে স্বস্তি দিন।,0,crime
আইন বলতে বাংলাদেশ কিছু নেই আমাদের দাবি রিফাত কে যেভাবে হত্যা করেছে ওভাবে অপরাধীদের হত্যা করা হোক যদিও ভাবে করা হয় তাহলে শিক্ষা হবে আর কখনো এ কাজ হবে না,0,crime
তার চোখ মুখে বলছে সে অপরাধী এরকম বহু করছে করতেছে বিধায় কেহ এটা নেটে ছারছে হ্যাকারা তার রুমে গিয়ে বসে ছিল আবুলের মত কথা।,0,crime
শেষ ভাল যার সব ভাল তার।,0,crime
দেশ প্রেম মানে কি দেশের জন্য কারা যুদ্ধ করেছিলেন তারা জদি আজ বাংলার অবস্থা দেখে তাহলে তারা নিজেই ফাশিতে ঝুলে আত্মহত্যা করতেন,0,crime
চাকরিবিধি লঙ্ঘন করলে একে বরখাস্ত করে শাস্তির আওতায় আনা হোক।,0,crime
নিজেদের লোককে নিজেরা কিভাবে বিচার করবে।লাশের উপর লাশ পরবে বাংলা বুকে। বিচার করার সাহস কারো নাই।কোপা সামসু বাংলা জনগনকে,0,crime
ভাইয়া আপনি অনেক ভালো,0,crime
ভালো ঐ নারীর বিচার করতে হবে তার তো কোন ছবি নাই কেন অপরাধ দুজনেই করেছে এক জনের ছবি দেখায় আরেক জন নাই,0,crime
রাতের বেলা অভিযান হলে ভালো হতো মুখোশ ধারী দের দেখা মিলতো,0,crime
মনে বড় জ্বালা রে পাঞ্জাবী ওয়ালা,0,crime
ভাই এগুলোতে এডিটিং করা যায় পাবলিক তো সব পাগল উনি একাই,0,crime
আমরা ফাসি চাই,0,crime
পুলিশ লীগের ফাঁশি চাই,0,crime
এই দৃশ্য আরো বেশী বেশী করে দেখান যাতে করে মানুষ এইসব হিংস্রতা থেকে বিরত হয়ে যায়।আর যত তারাতারি সম্ভব এদেরকে ফাঁসিতে ঝুলিয়ে মারা হোক।,0,crime
চোরের মনে পুলিশ পুলিশ আমরা বাংজ্ঞালী আমরা মানুষের চেহারা দেখলেই বলে দিতে পারি অপরাধী আর ভালো,0,crime
মিন্নি এই খুনের মুল নায়ক কিন্তু আপনি তাহা তুলে দরতে পারেন নি কলেজ থেকে বের হতে না হতেই মিন্নি এদিক ওদিক তাকাইতেচে এবং মনে মনে খুনিদেরকে খুজতেচে এবং কিচুখন পরে রিফাতকে যখন খুনিরা দরে নিয়ে যাইতেচে মিন্নি তখন সাভাবিক ভাবেই পিচেপিচে হাটতেচে এতেই বুযা জায় মিন্নি এ খুনিদেরকে লেলিয়ে দিয়েচে সামীকে মারার জন্য কুপাকুপি যখন পুরাদুরা চলতেচে মিন্নি তখন অভিনয় করে বলতেচে ওকে আর মেরোনা ও আমার সামী রিফাতকে হসপিটালে অন্যলোকেরা নিয়াগেচে কিন্তু রিফাতের বউ মিন্নি নিজের বাসায় চলেগেচে আর পুলিশের ইন্টারভিউ দেওয়ার জন্য রেডি হইতেচে পুলিশের জীগাসা বাদের সময়ও সামীর জন্য তার চোখে মুখে তেমন কনো কাহাউমাউ কান্না বুজা যাচচেনা আর কি বুজাবো আপনাদের কে,0,crime
পাপ কখনও বাপ কে ছাড়ে না নুসরাতে কান্নার আওয়াজ আজ ও কানে বাশে এদের দেখে আমাদের শিক্ষা নেয়া উচিত,0,crime
ভিডিও তে যা দেখা গেল তাতে পুরোপুরি ভাবেই মিন্নজড়িত,0,crime
তোমার জারি গান ভুল হয়েছে । কারণ স্ত্রীর পরিকল্পনায় স্বামীকে হত্যা করিয়েছে । ভাই গানটি সংশোধন করে আবার পরিবেশন করুন । ধন্যবাদ,0,crime
আমি ওতোকিছু বুযিনা আমার সেখহাসিনার কাছে একটা দাবি এই ভিডিওটা দেখার পরে আমার খুব কসটো লাগলো এই খুনের পিছনে মিননির পুরা পুরি হাত পুলিশ ভাইরা রিফাতের খুনিদের আগে মিননিরে আগে ফাসিদেন ভাইরা,0,crime
তুই তো নিজেই সব খুলে দিছা স্যারের দোষ কেমনে থাকবে,0,crime
ছুতা পারার দরকার,0,crime
ধন্যবাদ বাংলাদেশ সরকারকে কিন্তু ফাঁসির পর মিডিয়ার সামনে আনতে হবে জনগণকে দেখাতে হবে। আর কেউ যেন একটা না করে।,0,crime
এতগুলো মানুষ!! অথচ দেখে সবাই বাঁতাতে না গিয়ে চলে যাচ্ছে!!,0,crime
পুলিশ আদালত সব বন্ধ করে দিয়ে আপনার মতো লোকদেরকে নিয়োগ দেয়া দরকার। এতো বড় বড় গোয়েন্দা থাকতে কেন যে বাংলাদেশের এতো সমস্যা এখনো রয়ে গেছে বুঝতে পারছি না।,0,crime
অপরাদি জন্ম দিয়ে একন কান্না কিসের,0,crime
মিন্নি এই খুনের সাথে জড়িত। আমার প্রশ্ন তার স্বামীকে ওই ছেলে গুলো টেনে নিয়ে যাচ্ছে আর ওই মিন্নি ডান দিক বাম দিক তাকাচ্ছে কেন??? তার পর যখন তার স্বামীকে টেনে নিয়ে যাচ্ছে তখন সে তার স্বামীকে বাঁচাতে সে কোনো চেষ্টাই করলো না বরং সে আস্তে আস্তে ডান দিক বাম দিক তাকিয়ে তার স্বামীর দিকে গেল‌। আমি বুঝলাম না ডান দিক বাম দিক কি??? আমি বলতে পারি যে মিন্নি এই খুনের প্রধান পরিকল্পনা কারি। আমার আকুল আবেদন মিন্নির খুব তাড়াতাড়ি ফাশি চাই।।।।,0,crime
এতে কি মিন্নি ছিলো আর এখানে তো বলার কিছু নেই 😋 যায় আপনারা দেখেছেন আমি ও তাই আমি মিন্নির ফাশি চাই,0,crime
এইডা হাইস্যকর এমন জনি মার্কা লোক কোনো জেলার প্রশাসক হতে পারে না! এইডা হাইস্যকর,0,crime
এই খুনে মিন্নি ও জড়িত আছে,0,crime
মরনের কথা সরন করাে,0,crime
কান্দ কেন তুমাদের লজ্জা নেই বে সরম মহিলা,0,crime
অসাধারণ এক কন্ঠ খুব মেধাবী । কেন ঝড় নেমে এলো সুখের ঘরে ওহ,0,crime
তারাতাড়ি ফাঁসি দেন আমাদের বোনের আত্মার শান্তি পাবে,0,crime
দেশের জন্য মরন যুদ্ধ টাকার জন্য জীবন যুদ্ধ ৷,0,crime
গঠনা টি দেখে জা বুজলাম মিন্নি ই হুকুম দারি আসামি,0,crime
বাংলার জনগণ তুর পাগলা বুঝ বুঝে কাম হবে না,0,crime
আজকে তো মাথা ঠিক না থাকার কারনে ভুল করে লেখছে। ছুটি কি মন্জুর হইছে,0,crime
বেয়াদব মহিলা সব মেয়েটির দোষ,0,crime
এই সিসি ক্যামেরাটি কি কলেজের? যদি কলেজের হয়ে থাকে তাহলে এত লম্বা সময় ধরে ঘটনা ঘটলো পুলিশকে কেন খবর দেয়া হলোনা?,0,crime
এই ধরনের অপরাধিদের যদি সাথে সাথে শাস্তি দেওয়া হয় তাহলে অন্যরাও অপরাধ করতে কিছুতো হলেও ভয় পাবে।,0,crime
সজনদের কান্নাকাটি আমার কষ্ট হয় কি আর করা অপরাধ করলে তো সাজা ভুগ করতেই হবে পাপ কখনো বাপ কেও ছারে না,0,crime
আমি থেকে গ্যারান্টি যে এই মেয়েটাও জড়িত এদের সাথে বাট খুনের পরিকল্পনা ছিলো না হয়তো বাট মেয়েটা বলছ একটু আর নয়ন করে ফেলেছে অনেক বেশি যা খমতার অপব্যবহার আর আবেগ বাট এটা সত্যি যে মিন্নি এই ঘটনা টা আগে থেকেই জানতো এটা মিন্নিকে দেখেই বুঝা যাচ্ছে আর সে ভাবতে পারেনি তার স্বামী কে একবারে মেরে ফেলবে এই মেয়েটা চায়ছিলো এটাই স্বামী এবং প্রেমিক দুই জনের সাথেই সম্পর্ক ঠিক রাখতে আর এটা তার স্বামি চায়নি তাই হয়তো মিন্নি এবং নয়ন যুক্তি করছিলো রিফাস কে সাধারণ মানে অল্প মারার জন্য যেমন হাত পা ভেঙ্গে ফেলার জন্য এমনি একটা কিছু কিন্তু প্রেমিকা যখন বিয়ের পরেও স্বামিকে মারার অনুমতি দেয় তাও আবার আগের প্রেমিককে তখন কি আর প্রেমিকের হুষ থাকে থাকে না আর তা ছাড়া নয়নের ক্ষমতা ছিলো নেশা করতো আর আগেও সে এমন কিছু কাজ করছে তাও তার কিছু হয়নি তাই সে এই খুন করার সাহস পেয়েছে আর মিন্নিও ভাবেনি তার স্বামিকে একবারে মেরে ফেলবে তাই সে পরে বাঁচানোর চেষ্টা করে এবং মৃত্যুর পরে মানসিক ভাবে ভেঙ্গে পরে সবাই দাড়িয়ে না থেকে প্রতিবাদ করলে হয়তো ছেলেটা বেচে থাকতো মৃত্যুর ভয় না সবার এগিয়ে আসার ধরকার ছিলো কারন সবাইকে একদিন মরতে হবে,0,crime
আজকের অবৈধ মেলামেশায় নয় মাস পর যে বাচ্ছাটি জন্ম নেবে।সে হবে আওয়ামী লীগের বড় একটা নেতা।,0,crime
এই মহিলার বিচার হয়া উচিত,0,crime
এরা গরীব নীরিহ পেটের দায়ে হয়তোবা কারো প্রলোভন এ এই পথে!! ডিরেক্টার মেনেজার এদের সাক্ষাৎকার নেন। ভাল্লাগছে আপনারে আগে জানতেন তখন কই ছিলেন আউগারি মিডিয়া আপনারা,0,crime
ভাই এসব মেয়েদের জন্য একজন আরএকজনকে মারে ৷ সব দুষ মিনির,0,crime
মিন্নির কারনে আজ দুটো জীবন নস্ট হয়ে গেল,0,crime
মিন্নি জড়িত ফাসি হক,0,crime
একটা শয়তান শিরাজ কয়টা পরিবারকে ধ্বংস করে দিল,0,crime
আসসালামু আলাইকুম মহান আল্লাহ রাব্বুল আলামিনের কাছে দোয়া করেন যদি এই ঘটনা মিথ্যা হয় তার ফ্যামিলি যারা আছে এই দুনিয়াতে তাদেরকে মহান আল্লাহ রাব্বুল আলামীন পাকাবে আর সত্যের জয় অবশ্যই দুনিয়ার বুকে আপনারা পাবেন আপনাদের আহাজারি দেখে হৃদয়টা আমার চুরমার হয়ে যায় মহান আল্লাহ রাব্বুল আলামিনের কাছে আমি দোয়া করব আল্লাহ তুমি এই দুনিয়ার বুকে সত্য ঘটনা তুলে ধরে কি মিথ্যা তুমি ভালো জানো আমরা দূর থেকে কিছুই জানিনা আর নুসরাতের ফ্যামিলি ভালো জেনে নুসরাত কিভাবে মারা গেছে নো সাথে ভালো জানে প্রশাসনের উপর আমার বিশ্বাস আছে তারা যতই ভয় দেখাস না কেন আপনারা কেন মিথ্যা কথা বলছেন মরে যেতেন সত্যি বলতে তাদের ও দোষ দিব না তবে একদিন এই প্রশাসনিক সত্যের মুখ খুলবে হয়তো উপর দিকে কোনো বড় চাপ আছে,0,crime
আমার লেকাটা সবাই সেয়ার করবেন এ কিলিক করে পুরাটা পরবেন,0,crime
লোভে পাপ পাপে মৃত্যু।,0,crime
যদি সন্ত্রাসীদের বাঁচানোর জন্যই এই কথাগুলি বলা হয় তাহলে যে নয়নের সাথে তার বিয়ে হয়েছিল সে কথাগুলো কি মিথ্যে তার সাথে বার্থডে অনুষ্ঠানে তাকে দেখা গিয়েছে সেখানে তাকে কেক খাইয়ে দেয়া দেওয়া হয়েছে সেগুলো কি মিথ্যে তাকে রিমান্ডে নেওয়া হোক সব বেরিয়ে আসবে,0,crime
এগুলো হলো আগের রাতের ভোটের ফল,0,crime
সালা মিত্তা বলছে তার চোখের দেকেন,0,crime
এখন সবাই এটাকে গুজব বলে চালিয়ে দিলে কেমন হয় !!! 😆😀😀,0,crime
সে নিজে দোষি তাই তার মুখ দিয়া কথা বের হচ্ছে না,0,crime
বেটা লম্পট ঘরে রেখে বাহিরে দিকে নজর দিলে কেন।,0,crime
বালের বাংলাদেশে বাস করি আমরা।এত গুলা মানুষ তামাশা দেখে 😠😠,0,crime
সিসি টিভি ফুটেচ গুলা চেকক করলে তো হয় তা হলে তো সমাধার,0,crime
যদি কমেন্ট বক্সে হাসির রিয়েক্ট থাকতো তাইলে সবচেয়ে বেশি রিয়েক্টা আমি দিতাম😆😆😆😆😆😆😆😆😆,0,crime
এটাই কী আমাদের স্বাধীন বাংলাদেশ ওই ডিসি এর দালাল ছিল মনে হয়। একে ইসলাম ধর্ম হিসাবে সিরচ্ছেত করা উচিত,0,crime
পাপ বাপ কে ছাড়ে না দুই আগে বা পরে,0,crime
মিন্নির আসোল রুপ বেরিয়ে গেলো এবার কোথায় জাবে মিন্নির সাস্তি চাই তাহলে রিফাতের আত্তায় সানতি পাবে,0,crime
ফাসি হওয়া উচিত,0,crime
প্রসাসনে উচিত বাংলাদেশের প্রতিটা থানা ও ইউনিয়ন পর্যায়ের আওয়ামী নেতাকর্মিদের সম্পদের হিসাব নেওয়া হোক আমি জোর গলায় বলতে পারি আমার এলাকায় আজ থেকে বৎসর পূর্বে যে সব আওয়ামী নেতাকর্মিদের বাড়ীতে ভাত হত না এবং তাহাদের প্রকাশ্যে জীবিকার কোন আয়ের উৎস্য ছিল না। তাহারা আজ আলিসান বাড়ী দামী গাড়ীতে চড়ে বেড়ায়। দেখতে ভিশন খারাপ লাগে!!!! তাই বাংলাদেশ সরকারের উচিৎ এইসব নেতা কর্মিদের সম্পদের হিসাব নেওয়া। তাই আসুন দেশ তা আমাদের আমরা সবাই মিলে দূনীতিবাজদের মুখোস খুলে দিই সে যেই হোক বাংলাদেশ সরকার কিংবা আমি আপনি?,0,crime
এরকম অনেক জায়গায়ই বিবেকহীন পাচাটা কুৎসিত অযোগ্য দেশের ন্যায়নীতি ধ্বংশের কারিগরদের বসিয়ে রাখা হয়েছে!,0,crime
আর জেনো পাপ কাজ না করে,0,crime
সবই মনে হচ্ছে নেশাগ্রস্ত। প্রথমের মেয়েটা বুদ্ধিদীপত উওর দিয়েছে। হতাশায় নিমজ্জিত মানুষ গুলো এখানে। এরা দেখছি এক মুঠো ভাত খেতে যেয়ে ধরা খেয়েছে। লনচ ঘাট বা ফেরী ঘাটে এসব হতো আগে।,0,crime
মিন্নীরে ত্রখন কেনো আইনের আলতায় আনা হয়ছে না ওবারবার নয়নরে জরিয়ে দরতেছে স্বামীকে জোর করে দরে নিতেছে ওসাবাবিক বাভে হেটে যাচ্ছে ৷,0,crime
এম পি ছেলে কে দরে না কেন,0,crime
লুচ্চামি সবাই করে কেউ ফেঁসে যাই কেউ বেচে যায় কেউ ধরা পরে কেউ ধরা পরে না,0,crime
আরো ভাই ভয়ে এ সব কনছে?,0,crime
বালের তদন্ত রিপোর্ট ও বালের তদন্ত কমিটি এখন করা হলো ক দিন পর পাবলিক সব ভুলে যাবে ও তারপর দেখে শুনে টাকা খেয়ে তাকে আবার চাকরিতে বহাল রাখা হবে,0,crime
জান্নাতে আছে তালা🔒 জাহান্নাম হলো খোলা🔓 ~যদি চাবির সন্ধান চাও আযান শুনে নামাজে যাও। 🔑💯✅,0,crime
মিন্নীকে অবিলম্বে গ্রেপ্তার করা হক,0,crime
অপেক্ষায় আছে বাংলাদেশের কোটি মানুষ কবে শুনতে পাবো আমরা আবরার ফাহাদের হত্যাকারিদের ফাঁসির রায়।,0,crime
আমার শুনার বাংলা আমি তুমায় ভালবাসি,0,crime
নারীর। আমি এই জেলা প্রশাসক নারী লোভী এর বিচার চাই,0,crime
সাংবাদিক তুমি এখন নারী নখএ জানতে চাও আর এতদিন কোথায় ছিলা চাটুকার সাংবাদিক তোরা সাংবাদিক নামের কলঙ্ক,0,crime
ও মেয়েটা জে বাবে হাটে মনে আসামি দরিয়ে দিয়ে হারতেছে।ও জদি মনে করতো ওর সামিকে দরে নিয়ে জাচ্চে।তাহলে এবাবে হারতে পারতো না। কথা হলো ওকে আইনের আওতায় এনে। কঠিন সাজা দেয়া হোক।। তারপরে দেকবেন সবাই। সবকিছু বের হয়ে জাবে।।।।।,0,crime
রায় দ্রুত কার্যকর করার অনুরোধ,0,crime
আরে পুলিশ বইলা কথা এমন না হইলে হয় পাপে বাপরে ও ছাড়ে না,0,crime
যারা নেতা পরজায়ের ব্যক্তি তারা যদি এরকম খারাপ চরিত্র হয় তাহলে সাধারন মানুশ কি করবে,0,crime
কোনো হই চই আছে পরিবেশ টা ভালোনা ।😁,0,crime
কান্না কাটি করে লাভ নাই শুয়োর যে কাজ করেছিস ফাঁসিই একমাত্র উপযুক্ত শাস্তি ।,0,crime
আমি বুজিনা এরকম নষ্ট চরিত্রের লোক জেলা প্রশাসক হয় কিভাবে।,0,crime
ভিডিওতে প্রমাণ থাকার পরও আবার তদন্ত আর এ তদন্তের দায়িত্ব দেয়া হবে অপরাধীকে। বাহ এরকম তো ফানি ভিডিও তে হয় না।কোন নাটক বা সিনেমায় তো দেখলাম না কোন ভিলেনের কাছে দিতে। কিরকম একটা দেশে আমার জন্ম হলো!,0,crime
না মিন্নি জড়িত আছে হুম এটা এ সত্যি 😡,0,crime
কতই না ছটফট করে নুসরাত মারা গেছে আল্লাহ তুমি নুসরাতকে জান্নাত বাসী করিও আর ওর খুনিদের বিচার করিও।,0,crime
আমি ডিসি হবো ডিসি,0,crime
ভাই এটা জামালপুর এর মহিলা সেয়ানা পাবলিক মুখে এক কথা মনে আরেকটা,0,crime
চোর দরা পডার পর আবার মিডিয়ার সমনে আসে লজ্জা নাই তোর তো এতক্ষণে করে মরে যাওয়ার কথা 😡,0,crime
মিননির ফাসি চাই এটাই ভর খারাপ,0,crime
এটা কেমন তদন্ত অপরাধী তদন্ত করবে !কি তদন্ত করবে সেটা তো বোঝাই যাচ্ছে এরা জনগণকে বোকা বানাতে বানাতে এমন অবস্থা হয়েছে সি সি ফুটেজকেও মিথ্যা প্রমাণ করতে চায়।একবারও কি ভেবে দেখেছে আসলেই কি জনগণ এতোটা বোকা এখন তদন্ত করবে কে এই ভিডিও করে ছেড়ে দিয়েছে।এদের দেখলেও লজ্জা লাগে,0,crime
চোরের মার বড় গলা 😄😄,0,crime
বাংলাদেশে এই পথম খুনির বিচার হলো এবাভে বিচার হলে দেশে অপরাধ বারতোনা,0,crime
বাচ্চাটা বড় হলে ওর মার ফাসি হলে ভালো হত।,0,crime
লোভ সামলাতে পারে না টাকার কি না করে ইজ্জত দিয়ে চাকরি বাচাতে হয় খারাপ কাজ করেছো দোষ নাই ভিডিও করছে দোষ হয়ে গেল,0,crime
? ? এর সময় দেখেন যখন কুপানো শেষ তখন তার তার দিকে একবার এর জন্য না তাকিয়ে কোথায় চলে গেল ্‌্‌্‌্‌,0,crime
ছিহ একবারও তোরা ভাবলিনা নুসরাত ও তোদের মত একজন মানুষ। কারো মায়ের সন্তান। এবার তোরা মজা বোঝ।,0,crime
হেতিরা একটু ভালবাসাই তো করছে হেইয়া এত ভাইরাল করার দরকার কি ছিল। বাংগালির খাইয়া দাইয়া কাম নাই।,0,crime
নিহত রিফাত শরীফের এর স্ত্রী মিন্নী এখন পর্যন্ত কমপক্ষে বিভিন্ন টিভি চ্যানেলে বার এর ও বেশি সাক্ষাতকার দিয়েছে বার বার বলেছে আমি নয়নকে চিনি না নয়ন আমাকে ডিস্টার্ব করত এখন যে আমরা নয়ন আর মিন্নীর অন্তরংঙ্গ ছবি এবং কাবিন নামা দেখতে পাচ্ছি এগুলো কিসের আলামত সবাই একসাথে আওয়াজ তুলুন মিন্নী এবং নয়নের ফোন কল লিষ্ট চেক করা হোক মিন্নীকে বিচারের আওতায় আনা হোক ।।।,0,crime
দুই জনই সমান অপরাধী,0,crime
বৈতাল কে ধরে না কেন,0,crime
ফাসি চাই,0,crime
এটা মিন্নির প্ল্যান সিলো ভালোবাসার মানুষ ক নিয়ে যাচছে মারসে ওর কোনো ￰￰ফিলিংস নাই ও ভেবে সিলো নয়ন বন্ড তো পুলিশ থেকে পার পেয়ে যাবে ও যদি একটু বাচানোর অভিনয় না করে তাইলে ও ফেঁসে যাবে তাই নাটক করেছে রিফাত ক বাঁচানোর এত কোপালো তবুও মিন্নি স্বাভাবিক ভাবে ব্যাগ নিয়ে হেটে যাচ্ছে মিন্নি দোষী,0,crime
খুব তারাতাড়ি ফাঁসির আদেশ কার্যকর করা হোক,0,crime
অনেক ধন্যবাদ জানাই আমাদের প্রধানমন্ত্রী কে আমরা নুসরাতের হত্যাকারীদের ফাঁসির রায় শুনে খুশি হলাম। অতি তাড়াতাড়ি নুসরাত হত্যাকারী জানোয়ারদের পাশে অনুরোধ রইল,0,crime
হায়রে ডিজিটাল বাংলাদেশ শেখ হাসিনা এই উন্নয়ন করেছেন দেশের,0,crime
ভাগ সত্য তার বউকে কোন কুপ দেওয়া হই নাই তার বউ জরিতো,0,crime
এটা মিথ্যা নই সত্যি,0,crime
এই মেয়েটার মধ্যে দোষ আছে এবং মেয়েটাকে আইনের আওতায় আনা হোক তার পরে বুঝবেন ডাল মে কুচ কালা হে,0,crime
শেখ হাসিনা কি করছেন তিনি খুনিদের এখনও ফাসি দিচ্ছে না কেন? আমি ঘৃনা করি এই বাংলাদেশকে। এবং বাংলাদেশের আইন ব্যবস্থাকে।,0,crime
প্রশ্ন একটাই যারা উচ্চ পদস্থ তদন্ত কমিটি হবে উনারা হয়তো দুধে ধোয়া তুলসী পাতা হবে। সত্য মিথ্যা যাই হোক পাপের বোঝা ভারী হলে এমনি হয়। তবে আমি সাধারন নাগরিক হিসেবে মনে করি থানা থেকে শুরু করে জেলা বিভাগ পর্যন্ত প্রত্যেক কর্মকর্তার অফিসের সহকারীদের চাকুরী যোগদান করার পূর্বে সম্পত্তির হিসাব রাখা জরুরী । বিশেষ করে প্রশাসনীক কর্মকর্তাদের ।,0,crime
কেমেরা তুমি বসাইছো।,0,crime
বাংলার সিনেমার মতো খুন হওয়ার পর পুলিশ আসল,0,crime
ধন্যাবাদ ভাইয়া,0,crime
আমারা বিছার চাই,0,crime
তোদের দুইজনকে লাঠি পিঠা করে মেরে ফেলা দরকার,0,crime
স্যারের সোনাই ঘুম নাই হারবাল খাওয়ানো উচিত,0,crime
ভাই অারবার ভাই এ র খুন নিয়ে একটা ভিডিও দেন প্লীজ,0,crime
রিফাতের বউকে ফাঁসি দেওয়া উচিত,0,crime
শুধু ডিসি একা নয়! ওই মহিলা ও জগন্য,0,crime
ভাই এসব লিলা খেলা,0,crime
রিফাত ফরাজীর বিচার হলো রিফাতকে ও যেভাবে কুপিয়ে হত্যা করেছে ওকেও একদম এভাবে প্রকাশ্যে কুপিয়ে হত্যা করতে হবে। আার স্বামীকে কোন মানুষ কিল ঘুষি মারতে থাকলে কোনো স্ত্রীর হাঁটার স্টাইল এমন হতে পারেনা!!ভিডিওটা দেখে সত্যিই অবাক হলাম!!!!!,0,crime
মিনিট হবে কেন ডিসি সাহেবের ভিডিও হয়েছে মিনিট সেকেন্ড আমার কাছে পুরা মিনিট সেকেন্ডের ভিডিও আছে আর আপনার এখানে দিয়েছেন মাত্র মিনিট বাকি ভিডিও কোথায় রাখছেন আপনাদের বাড়িতে নাকি,0,crime
জানতে চাই জানতে চাই এত সুন্দর ছেলে কে মারা হলো কেন,0,crime
জীবনে এই প্রথম দেখলাম। মানুষকে মারতে দেখে মানুষ পালিয়ে যায়। দেখি সিংহের সাথে বন গরু যুদ্ধ করে তার সাথিকে বাঁচাতে।,0,crime
কোন নুসরাত মৃত্যু হয়েছে প্লিজ বলবেন।,0,crime
লজ্জারে আসলে মানুষ কতজন ওর বউ মেয়ে হয়তো আছে তারা দেখে হাত মারবে আর কি,0,crime
ভাল থাকেন আপনাৱ কিছু হবে না জানি আল্লাহ বিচাৱ কৱবে ইশাললাহ আপনাদেৱ,0,crime
বঙ্গবন্ধু কন্যা শেখ হাসিনা তিনি এমন একজন লোক যার কথা মুখে বলে শেষ করা যায় না পুলিশের ওসি ডিসি মন্ত্রী এমপি ছাত্রলীগ কুত্তালীগ গুরু লীগ এখন আবার বের হয়েছে বদমাইশ লীগ লুচ্চা লেগ বেশরম লীগ ধর্ষণ লীগ তদন্ত লিক ।,0,crime
ধন্যবাদ সরকারকে উৎখাত করতে ।,0,crime
আমি চাই রিফাত ফারাজী ও মিন্নিকে আগামী ঘন্টার মধ্যে গুলি করে মারা হোক,0,crime
সরাসরি গুলি করে মারা হোক,0,crime
কি সুন্দর কথা! স্যারের কুনু দোষ নাই। যা দেখলাম ভিডিওতে এখনো অামার ইয়ে নরম হচ্ছে না 😁😋🙄,0,crime
মরে যা তদের বাঁচার ওদিকার নাই,0,crime
দেখে মনে হচ্ছে মিন্নি নাটের গুরু,0,crime
যারা নুসরাতের হত্যা করেছে সে হোক বিএনপি ও আওয়ামী লীগ যে দলেরই হোক না কেন তাদের যেন ফাঁসির রায় কার্যকর হয় তাহলে আমরা খুশি হব দেশবাসী এরপর মনে করব বাংলাদেশে এখনও বিচার আছে এধরনের আসামিরা আইনের ফাঁক দিয়ে কখনো যেন বাঁচতে না পারে,0,crime
বাকি আসামিদের মুখের কথা সুনতে চাই,0,crime
ধন্যবাদ ভিডিওর জন্য।,0,crime
অপরাধের সময় মনে ছিলো না আল্লাহর নাম,0,crime
সবার মন্তব্য সঠিক হয়েছে মিন্নি জরিত। আর একটা বিষয় মিন্নি শুধু নয়ন কে আটকাচ্ছে কারন সে নয়ন কে ভালবাসে। আর এটা পরিকপ্লিত,0,crime
নাইস,0,crime
আসল খুনি মুনি,0,crime
নয়ন বন্ধ যদি আমার ভাই হতো তাহলে আমি নিজেই ওকে মেরে ফেলতাম। যে কাজটি নয়নের মায়ের করা উচিত ছিল। ! কারণ তার একটা কুলাঙ্গার সন্তানের জন্য অন্য মায়ের কোল খালি হবে কেন। ? আর কুকুর যদি পাগল হয়ে যায় সেই কুকুর টি মেরে ফেলাই বেষ্ট !,0,crime
এই মিন্নি দায়ি ওকে কেন পুলিশ দরছেনা,0,crime
বালের অভিনয়,0,crime
নাম্বার বন্ধ,0,crime
এইযে অপমান। এই যে কলংকো। কেমন কোরে সমাজে মুখ দেখাবে।একে তো তালাক দেবে । সুখের সংসার ছেলে মিয়ে চাকরি সব হারিয়ে এখুন একা হোয়ে যাবে। কি লাব এসব কোরে কেনো মানুষ বুঝে না।,0,crime
ফাঁসি কার্যকর দেখতে চায় জনগণ।,0,crime
সব কয়টা পাল্তু এভাবে নাটক করবেন না,0,crime
এখানে তদন্ত করার কি আছে সব প্রমান ভিডিওতেই। তদন্ত করতে গেলেই সত্যটা মিথ্যে দিয়ে ঢেকে দেওয়া হবে।,0,crime
মিথ্যা কথা বলেছে মিন্নি এই খুনের সাথে মিন্নি ও জড়িত আছেন,0,crime
জয় বাংলা জয় বঙ্গবন্ধু শেখ মুজিবুর রহমান যে বঙ্গবন্ধু দেশের জন্য জীবন দিয়েছে সেই দেশে এত খারাপ লোক ভাবতেও অবাক লাগে,0,crime
এইটা হাসিনার ডিজিটাল অফার।,0,crime
হে রাইট মিন্নিকে ও নাম্বার আসামি করা হোক কারন ইসপস্ট দেখা যাচ্ছিল মিন্নির ও হাত আছে,0,crime
এইটার নির্মাতা নিশ্চিত গাজা খোর,0,crime
তারাতারি ফাসি দেয়া হোক তাদের,0,crime
আমি অনেক দেখেছি এই দেশে সুদু রেবেএ পারে আর পুলিশ জনগনের ভাল পালায়,0,crime
তাও মাথায় টুপি টা আছে আহাহাহা শয়তানের কিরূপ,0,crime
শুধু একতর্ফা ডিসির দোষ দিলে ভুল হবে।মহিলা নিজেই আগে থেকে রেডি হয়ে আসছিলো।বোরখার নিচে সেমিজ ছাড়া কিছুই পরেনাই।পায়জামা ও না।একটা মেয়ে প্রশ্রয় না দিলে পুরুষেরা কখনো এইসবে লিপ্ত হতে পারেনা।,0,crime
স্যারের দশ নাই তোমার নাই কাম টা করছো কি,0,crime
আসামী মিন্নি কে গ্রেপ্তার করা হোক অভিনয় করে বাচা যাবে না।,0,crime
ওপরাদি জেই হোক না কেনো। আমরা প্রবাসিরা এর সঠিক বিচার চাই।,0,crime
মিনিটে জ্ঞান হারায়নাই এখন কিছু না হইতেই বেহুস !,0,crime
কি ভাবে আমাদের নারীরা চাকরি করবে জানিনা।,0,crime
মিন্নি জরিতো আছে,0,crime
ভাই বনি আমিন তার নাগরিকত্ব ত্যাগ করেছে।কারণ এসব লুচ্চামি ভন্ডামি রোধ করার ক্ষমতা তো আমার মত ম্যাংগো পিপুলের নাই বাধ্য হয়েই দেশ ছারতে হবে।তোরা থাক তোদের ডিজিটাল দেশ নিয়ে!!সেইসব মেয়েদের নিয়ে আফসোস হয় যারা নিজের ইজ্জতকে ভূলুন্ঠিত করতে কুন্ঠাবোধ করেনা!! এই নারিই তো কারোনা কারো মা অথবা বোন। আজ মনে এদেশে জন্ম না নিলেই ভাল হত অন্তত রক্ষকবেশী ভক্ষকদের রাশলিলা তো দেখতে হতনা!!!,0,crime
নিরপরাধ মেয়েটার কস্টের চিৎকারে তখন আকাশ ভারী হয়ে গিয়েছিল তখন তোরা কোথায় ছিলি,0,crime
কোন অপরাধের বিচার হয় না দেইখা দিন দিন অপরাধীর সংখ্যা বৃদ্ধি পায়তাছে ।,0,crime
মেয়েটা দুষি,0,crime
মেয়েটা কি বিবাহীত,0,crime
আল্লাহ এদের বিচার করবে না তোমরা যে সন্তান মানুষ করছো সন্তানকে কোন তরিকায় মানুষ করছো এই হিসাব দেয়া লাগবে কাল হাশরের মাঠে বিচার হবে না তোমাদের বিচার হবে তোমাদের সন্তান,0,crime
এই গুলো দেখে অ মানুষ রা সিক্ষা নেক যেতে অপরাধ করার আগে পরিবারের কথা ভাবে,0,crime
এত সুন্দরী কম বয়সী মেয়ে পেয়েও বাইরে চোখ যায় রুচিই খারাপ,0,crime
দুজনের দেহের সাধ মিটিয়ে গেছে,0,crime
জুতা পেটা করা উচিত।,0,crime
কে কে চান বিচারের কার্যক্রম দ্রুত গতিতে শেষ হোক সবগুলোকে অতি দ্রুত পাশি দেয়া হোক। শুধু রায় হলে হবে না মানুষ রায়ের কার্যকারিতা দেখতে চায়,0,crime
ভাই বলার ভাষা নাই আমার কাছে,0,crime
শিক্ষিতরা জাওরা,0,crime
কি একটা অবস্থা নিজের লুচ্চামি নিজেই তদন্ত 🙄,0,crime
যতজন জড়িত তাদের সবাইকে কঠিনতর কঠিন শাস্তি দেওয়া হোক,0,crime
কে করবে কার বিচার বাংলাদেশের শব নেতা খেতা এমন কি দেশের প্রধান শে নিজেও অপরাধী,0,crime
মিন্নীর ফাশিঁ চাই,0,crime
এই মেয়ে ফাসি চাই,0,crime
আমি বুঝতে পারছিনা এতো ছোটো মাপের বদমাস বাংলাদেশের মানুষ স‌হ‍্য করলেন কিভাবে। দুঃখজনক বেপার।,0,crime
সটিক কথা বলচেন বায়,0,crime
ওকে দেখে লুচ্চাই মনে হচ্ছে,0,crime
এসব অপরাধীর পক্ষ না নিয়ে বরং তাদের অপরাধের জন্য মনে মনে ঘৃণা করা উচিৎ।,0,crime
মেয়ের সর্বোচ্চ শাস্তি মৃত্যু দন্ড চাই,0,crime
স্বামীদের জে কেমনে বিস্বাস করব আল্লাহ জানে,0,crime
মিন্নির ফাসি হওয়া উচিত!! মিন্নি এই হত্যাকান্ডের প্রথম আসামি!! এই ভিডিও তার বড় প্রমাণ প্রশাসনের দৃষ্টি আকর্ষণ করছি!! !!😡😡😡😡,0,crime
বাংলাদেশের মধ্যে যতটা ক্লাব আছে সব ক্লাবের মধ্যে জুয়া খেলা হয় যে মানুষগুলো জুয়া খেলা খেলতেছে সবাইকে বছরের সাজা দেওয়া হোক কারণ তারা কখনো জুয়া খেলা ছাড়তে পারবে না,0,crime
তদন্ত কি সরাসরি দেখা যাচ্ছে কাম চলিতেছে। বলনা আমি অসুস্থ তাই কাম ঠিকভাবে করতে পারি নাই। তাই এটা আমার বিরুদ্ধে ষড়যন্ত্র। আমি তো কাম করি নাই। শুধু চুম্মা দিছি।,0,crime
লোভী মহিলা টাকার জন্য কুকাম করতেও দিদা করে না,0,crime
একটা কথা বুঝলাম না লোকটা এমন কি করেছে মেয়েটা তার রুমে গেল কেন মেয়ে তো রাজি ছিল,0,crime
দেশের হাজার হাজার মানুষ মারা হচ্ছে এদের কোনো বিচার নাই শুধু নুসরাতের বিচার হচ্ছে কেন,0,crime
মিন্নী কেন কলেজ ফাকি দিয়ে প্রতিদিন নয়নের রোমে যেত ? আর মিন্নী বলছে নয়ন বিরক্ত করত আসলে মিন্নীকে রিমান্ডে নিলে খুনের রহস্য বের হয়ে আসবে । আর রিফাত ফরাজিকে কেন এখনো বাচিয়ে রাখা হয়েছে?,0,crime
ক্ষমতার আসনে যোগ্য নেতা নেত্রী না থাকলে ঐ সমাজ আর ভালো থাকে না। এটা তো আল্লাহ তালার বাণী।,0,crime
এখানে কটের কিছুই নাই পাপ বাপকেও ছাড়ে না এটাই সত্য,0,crime
একটা স্বামীর কাছে এটা খুবই দুঃখজনক মরার অাগের স্ত্রীর শয়তানি রূপ দেখা 😢😢😢,0,crime
এইটা হচ্ছে বড় ধরনের ধর্ষণ,0,crime
বাংলাদেশে আইন বল কিছু নাই।,0,crime
এরচেয়ে বেশি কষ্ঠ পেয়েছে নুছরাত ও তার পরিবার ও পুরো দেশবাষি অতএব যত তারাতারি সম্বব ফাঁসি কার্যকর করা হোক তাহলে নুছরাতের আওা শান্তি পাবে।,0,crime
জেলা প্রসাসোক বোলে কোনো হোইচোই নাই এই ঘটোনা জোদি কোনো দারিওলা বা লেভাজ ধারি কেউ কোরতো এতোকখোনে তারে রিমানডে নেয়া হোতো আরোকতো কি,0,crime
অপরাধী দের জন্য যারা কান্দে তাদেরকে ও আইনের আওতায় আনা জুরুরি,0,crime
জুতা মারো ডিজিটাল শয়তানের মুখে,0,crime
এটাই বাংলাদেশ😂😂😂😂,0,crime
যেমন কর্ম তেমন ফল,0,crime
এই মহিলার বিচার হওয়া উচিত,0,crime
ভাই যে ব্যক্তি সেই ঘরের মধ্যে সিসি ৎক্যামেরা ফিট করেছে তাকে নোবেল পুরস্কার দেওয়া হোক আমার সাথে কে কে একমত,0,crime
এই দেশে কোনে শুষ্টো বিচার নাই,0,crime
ডিসির রিযিক নষ্ট করল ছিছি দিয়ে কে এই কামডা করল,0,crime
নারীবাদীদেরকে উচ্ছেদ করতে হবে। নয়তো এদেশে পূরুষের অধিকার বলতে কিছুই থাকবে না।,0,crime
এদেরকে ও জেলে ঢুকান হোক। অতিদ্রুত ফাসি দেওয়া হোক।,0,crime
সসরকারকে এসব বিষয় আইন করা উচিত,0,crime
মিন্নি ও জড়িত আছে ভিডিও দেখি মনে হয়,0,crime
পুলিশ ও জরিত থাকতে পারে তা না হলে নয়ন এত গুলো মামলার আসামি সে কি ভাবে ঘুরে বেড়ায় পুলিশ জরিত আছে পুলিশের বিচার করা হউক,0,crime
এরা করলে তদন্ত হবে আর বিরুদিকেও করলে দেশোদরহি হবে তাইনা আসোলে বাংলাদেশে এখন সাংবাদিক নামে জারোগ সন্তান বরেগেছে আল্লা তুমি এদের হাতথেকে আমাদেরকে রক্ষাকরো,0,crime
এখন আর কমেন্ট এ কেউ হিগাব কই মাগি বলবে না😂,0,crime
কোপ্পা সামচু,0,crime
মিন্নি হত্যার সাথে জড়িত,0,crime
সারে ওনাকে দুচে দিছে সারের কোন দোষ নায়।আললাহ হেদায়েত দান করুক,0,crime
আজ ভালো লগছে ভাই,0,crime
বোরকা পরলেই যে মেয়েটি ভালো হবে তা নয় তার কি দোষ সে ঈদের কোলাকুলি করেছিল ☺️,0,crime
আসলে এই গটনাটা যদি মেয়ের না করে ছেলে করতো তাহলে আজ দেশে দেশে নারী নির্যাতন কত মামলা হতো আর কত কাহনী করতো আসলে মেয়েটা মনে হয় রাস্তার পতিতালয় জন্ম হয়ে ছিলো,0,crime
ভারতে যদি এইরকম আইন তৈরী করে তাহলে খুব ভালো হয়,0,crime
ভাই পুলিশ এখনো কিভাবে চুপ করে বসে আছে এইসব সিসিটিভি ফুটেজ দেখে আমি বুঝিনা কিছু যতোটুকু বুঝলাম এই হত্যাকাণ্ডের সাথে এই মেয়েটি জড়িত,0,crime
মিস্টি বিতরন করা উচিত ফাঁসির দিন🙌🙌🙌🙌🙌🙌🙌🙌🙌🙌🙌🙌,0,crime
সকল মা তার সন্তানের জন্য অন্য রকম একটা মমতা কাজ করে কিন্তু যে মেয়ে টাকে আপনার ছেলে মেরেছে এত নিমম ভাবে চিন্তা করেন সে মায়ের কতটা কষ্ঠ হয়েছে আপনি সে মায়ের জায়গা থেকে চিন্তা করেন তাহলে আপনার কুলাঙ্গার ছেলের কথা মনে পডবে না,0,crime
চরিত্রহিনরা রাজনিতি করে ফাক বাংলাদেশ,0,crime
মন্ত্রীর মন্তব্য শুনে আমি মুগ্ধ এখানে বলা হচ্ছে তদন্ত করতে সিদ্ধান্ত নিবে মিনিটের পর এখানে আর কি বাকি থাকে এখনকি ডি এন এ টেস্ট করতে হবে না,0,crime
আপনার স্যারের কোন দোষ নাই আপনার দোষ নাই দোষ হলো আমরা যারা দেখছি তাদের আমাদেরকে সবাই মিলে এখন বিচার করেন,0,crime
মিননিকেও আইনের আওতায় আনা হোক,0,crime
ধন্যবাদ আদালতকে,0,crime
গোসোল করতে জাইতেছে আনটি,0,crime
পর্দাশীল মহিলা।,0,crime
উনি মনে হয় হিজাব অবসেসড 😂,0,crime
না জেনে কাহাকে খুনি বানানো ঠিক না।এই খুনের সাথে এমপির ছেলে জরিত।,0,crime
তোর মতো মা বাঁচার দরকার নাই যার বাচ্চা থাকার পর ও অন্য পুরুষয়ের সাথে খারাপ কাজ করে চি চি,0,crime
আহহ বিনুদুন! ব্যাপক বিনুদুন মূল ভিডিও তা কবে পাওয়া যাবে এই ব্যাপারে ডিসি কিসু বলেসে,0,crime
রিফাত কে কেন মারা হল,0,crime
এতো আবেগ দিয়ে উপস্থ্াপনের কি এটা। ওরা নিজের হাতে কোন মানুষের গায়ে কেরোসিন ঢেলে আগুন দিলো ঔ মন টা নিয়ে ফাঁসি হচ্ছে। এতো ডং করে এসব আসামিদের উপস্থাপন করবেন না দয়া করে।গর্দানতো ডাইরেক্ট কাটা হয়নি।সেটা হলেই উত্তম হতো।,0,crime
নয়নের সঙ্গে রিফাত শরীফের আগে কোন শত্রুতা ছিল না এই মিন্মির কারণ রিফাত শরীফ খুন হয়েছে কারণ আপনারা দেখেন একজন হয়ে দুজনের সঙ্গে খারাপই করেছে অর্থাৎ এক বধু দুই স্বামী এই মেয়েটা রিফাত শরীফের সঙ্গে বিয়ে না করলে এই খুনটা হত না এই মেয়ের সম্পূর্ণ অভিনয় করছে এই অভিনয় দেখে আপনারা ভুলবেন না নষ্ট মহিলা এই দুই খুনের দায়ী এই মেয়েটা তাই আমি বাংলাদেশের আইনের কাছে এই মেয়ের এমন শাস্তি চাই বাংলাদেশ এমন কাহিনী যেন না করে মৃত্যুদণ্ড আপনারা দেখেন এই মেয়ে টি যদি বিয়ে না করতো রিফাত শরীফ মরতো না এবং নয়নো এভাবে মরতো না দুজনই তো মারা গেছে এ কে বাঁচিয়ে রাখে লাভ কি একই মৃত্যুদণ্ড দেওয়া হোক,0,crime
দেখে খুব খারাপ লাগলো এতো মানুষের সামনে একটা মানুষ কে মারলো আর সবাই শুটিং দেখলো ছি ছি,0,crime
এখন কেমন লাগে! যখন নুসরাতকে মারছিল,0,crime
সত্যি গটনায় তদন্ত কিসের অপরাদিকে ছেড়ে দেওয়ার নামে যদি তদন্ত হয় তা হলে তদন্ত না করাই বালো এর বিচার চাই,0,crime
কান্না করে লাভ নাই।।এইখানে কেউ মিথ্যা কথা বলে নাই।।।আল্লাহ দেখিয়ে দিলো।।তার চাইতে নুসরাত বোন বেশি কান্না করেছে।।একা মেয়েটাকে সবাই এতো কষ্ট দিয়ে মেরেছে।।আমরা দেশবাসী দেখতে চাই।।ওদের কষ্ট।।।।,0,crime
ডি সি সাধনা করতেছে হায় ডি সি সুন্দর বউ থাকতে কেন যে সাধনা করতে গেলি,0,crime
তুমড়া এখন কেন কাঁদছ কেঁদে কুনু লাভ নেই ।অপরাধির সাস্থি হবে এটা আমাদের সবার কাম্য,0,crime
নুসরাত ও কেঁদেছিলো,0,crime
আমি একজন ভারতীয় মুসলমান বলছি যে বাংলাদেশ মুসলমান দেশের মধ্যে এত যে অন্যায় নোংরা কাজ এবং মুসলমান মুসলমানের মধ্যেই সীমাবদ্ধ তাই আমার অনুভব যে কিয়ামত কি বাংলাদেশ থেকে শুরু হবে ?,0,crime
এই মহিলাকে বাস দেৱা হক,0,crime
অতিদ্রুত নুসরাত হত্যার বিচার চাই,0,crime
হুম মহিলারেও ভাল করে তদন্দ করা দরকার কারন কিছুদিন পরে দেখা যেত এই মহিলাই ডিসির বিরুদ্ধে ধর্ষণ মামলা করত আর ডিসি রে সরকারি সব চাকরি থেকে বরখাস্ত করা হোক,0,crime
কতবড় মিথ্যা বাদি অসিকার করে মনে হয় মিথ্যা কথার উপর সরকার ভাতা দায়,0,crime
শাওন মিয়া,0,crime
সবচেয়ে বড় লজ্জা হলো শালার বেটা আবার মিডিয়ার সামনে কেমনে বড় কথা বলে। ওরতো বনবাসে যাওয়া উচিত।,0,crime
চখের পানি দরে রাখতে পারলাম না,0,crime
ভাই কিছু কিছু টকশো হরেছে কিন্তু ডিসি সাব জেনো বেচেজা এরকম,0,crime
রিফাত কে ধরে এনে রিমান্ডে নিয়ে। তার সাতে কে কে জরিত। তদন্ত করা হক।,0,crime
? থেকে ? দেখলে বুঝা যায় মিন্নি কি এ খুনের সাথে জড়িত কিনা। মিন্নির হাটার ধরন দেখলে বুঝা যায়,0,crime
কোন দেশেতে বাস করি আমরা কেউ অপরাধ না করেও অপরাধী আবার কেউ আকাম করে আবার নিজেই নিজেরটা তদন্ত করে সে অপরাধী কিনা থু থু থু এসব কুত্তাগো কপালে স্বাধীনতার চেতনা এমন ভাবে চাতায় দিছে যে থামায়তে না পেরে নিজ অফিসের কর্মীর সাথে আকাম করে,0,crime
মাননিয় বিচারকমন্ডলির কাছে আবেদন এরাযেন বাছতেনাপারে,0,crime
মজা তুমিও পাইছো ও পাইছে! এখন এই সব বলে লাভ কি,0,crime
মিনিন আসল অপরাধী ও জন্য দুইটা ছেলে খুন হলো মিনিন দুই জন কে বিয়ে করেছে মিনিন কি চেয়েছিল এটা দেখা যাক এখন কাকে খুন করবে,0,crime
জাতী একটা কথা জানতে চাই এই কমেন্ট বক্স কি জন্য রাখা হয়ছে? জাতী মিনিট সময় নস্ট করার জন্য নাকি কমেন্টের পতিকৃয়া অনুযায় ব্যবস্থা নেয়ার জন্য?,0,crime
ভাবিয়া করিও কাজ মাল খাবাই ভাবিও না বোন,0,crime
এখনো সে ওই পদে বহাল কেনো আছে জাতি জানতে চাই আমাদের জামালপুরের মান সন্মান আর রইল না,0,crime
ওর মাথায় ডেলে দিব নাকি,0,crime
নিজের বিরুদ্ধে অভিযোগ নিজেই তদন্ত কররে।নিজেই বিচার করবে,0,crime
ডিসি যে কি একটা বিপদে পড়ছিলো,0,crime
এই সব মেয়েদের কারনে সব মেয়ের দোষ দেওয়া হই,0,crime
ডেলে দিই🍷 ডালের যে তখন হুশ ছিল না এখন বলে স্যারের দোষ নাই😖 ঠেলে দাও ডেলে দাও এটা বর্তমানে নীতি হয়ে গেছে😆 হায় রে বাংলাদেশ😭,0,crime
রিয়েলিটি ছিলো মেয়েটার চোখে এক্টা ক্ণা পড়েছিল সেটা প্রসাশক ছাহেব ফু দিয়ে বের করছিলেন,0,crime
যারা কান্নাকাটি শুরু করেছো তারা কি একবার চিন্তা করেছো যে নুসরাত কতো কষ্ট করে কাতরাতে কাতরাতে মারা গেছে তখন কই ছিলা তোমরা ??? এখন কোন লাভ নাই ????,0,crime
বেটা তুইও ডিসির দালাল,0,crime
এ রকম সব অপরাধের বিচার হলে আমার দেশ সোনার দেশ হবে।বিচার হয় না বলে এ দেশে এতো পাপ হয় অপরাধ হয়।অপরাধিরা বলে খুন করলে ও আমি মুক্তি পাবো। কারন তারা জানে আমাদের বিচার হবে না।ধন্যবাদ সরকারকে নুসরাতের বিচার করার জন্য।এই ভয় অপরাধীকে অপরাধ করতে বাধা দিবে।।,0,crime
আইনের কাটগড়াই দাড়নো করা হুকো মিনিকে,0,crime
আরে মিন্নিকে ফাঁসি দেয়না কেনো আর ভালো লাগে না,0,crime
রিফাত ফরাজীর মৃত্যুদণ্ড চাই আর মিন্নি সুন্দরবনের রিমান্ড চাই ।😂😂😠😠,0,crime
ওসির সব ধরনের সজোগ সুবিধা বাতিল করা হোক এবং তাকে অতি তারা তাড়ি বিচারের আওতায় আনা হোক কারন সে পুলিশের পবিত্র জায়গা কে অপবিত্র করেছে।,0,crime
আমি অবাক হলাম এইটা দেখে যে এতো মানুষ ছিল ঘটনাস্থল এ কিন্তু একজনও বাধা দিলনা হায়রে মানুষ,0,crime
ভিডিওটিতো আর মিথ্যে না।,0,crime
মহিলার স্বামী কইরে,0,crime
দেশটা কি হয়ে গেল,0,crime
আগে মানুষ এর মতো মানুষ করতেন তাহলে এই রকম রাস্তা শুয়ে শুয়ে কাঁদতে হতোনা,0,crime
হায়রে কুলাংগার ভীরু কাপুরুষ বাঙালী সাহস করে কয়েকজন এগিয়ে গেলে শয়তানেরা এমনটা করতে পারতো না এতে মা তার সন্তান হারা বোন তার ভাই হারা হতো না,0,crime
জড়িত খুনি সবাই কে কঠোর শাস্তিদান করা দরকার যারা জড়িত রিপাত হত্যায় তাদের সবাইর কঠোর শাস্তি জরুরী মিন্নিকে যারা দোষী বানাতে চায় ঐ খুনিদের সহযোগী অথবা বাহিনীর সদস্য তাদেরকে ও শাস্তি দেয়া উচিত একটি মেয়ের মান সম্মান হানী করতে মিথ্যা অভিযোগ করার দায়ে তাদের শাস্তি ও দরকার,0,crime
মিন্নির লজ্জা থাকা দরকার,0,crime
বেয়াদব একটা,0,crime
কুন করতে মজা লাগে একন পাসি হবে একন নানান দরনে কথা পাসি চাই,0,crime
আমি তো আজ হেরে যাই নি হেরে তো গেছি সে দিনি যে দিন আমার জম্ম বাংলাদেশ নামক এমন একটি দেশে জম্ম গ্রহন করেছি তাই তো জিতার স্বপ্ন চেড়েই দিলাম জীবন বাঁচাতে বড় দায়। সব দোষ আমাদের প্রবাসীদের দেয়া হত আমরাই বড় খারাপ আর এখন প্রতিদিন বড় বড় ডিগ্রি ধারী মোড়লদের কর্মের বড় বড় সুফলের খবর দেখতে পাই। ধিক্কার জানাই সেই সব মানুষ গুলোকে যারা সোনার বাংলাকে কুল্সিত করে বিশ্বের দুয়ারে।আমার আগামী প্রজম্মকে কোন শিক্ষার আলো দেখাবোনা যেন শিক্ষিত হয়ে এমন কাজ না করতে পারে শিক্ষিত হোক সেটা চাই না চাই অশিক্ষিত এক জন সৎ মানুষ রুপে।।।।।।।। ধিক্কার জানাই তোমাদের। ছিছিছি।,0,crime
এখনো কেন ঐ মিননি কে গেপতার করা হয় না সব কিছু মিননির কারনে হয়েছে যখন দরে নিতেছে তখন মিননি কিছু করে নাই সাবাবিক ভাবে হেটে যাচ্ছে আমি খুনি মিননির ফাসি চাই,0,crime
এখন কান্না কর কেন মনু রা সুন্দর নুসরাত আপি টা কে ক্ষুন করার সময় মনে হয় নাই তোমাদের একদিন এমন পরিনতি হতে পারে,0,crime
ভারতে যেভাবে ধর্ষণ খুন রাজনীতির খুন এসব হচ্ছে ফাঁসির সাজা থাকলে এত খুন হতো না,0,crime
হাসি পায় বেলয্যা রা,0,crime
এখনো চেহারা দেখায় কেমনে!! আবার সংবাদ সম্মেলনও ডাকে লজ্জার লেভেল কতো নিচে থাকলে সবার সামনে এসে বলে তদন্ত করে দেখবে!!,0,crime
জেলা প্রশাসক যদি করে এমন ভয়াবহ অপরাধ তাহলে বাকিরা কিরবে কি এদের কি শাস্তি হওয়া উচিৎ আমার মতে দুইজনকে চাকরি থেকে বাদ দিয়ে বিয়ে দিয়ে দেয়া উচিৎ,0,crime
আমি জ্ঞান হারাবো মরেই যাবো বাচাতে পারবেনা কেও পড়েনা চোখের পলক কি তোমার রুপের ঝলক,0,crime
ভালো হয় নাই,0,crime
টিপু ভাই বাংলাদেশ বাংলাদেশে সরকারি চাকরিজীবি আছে তাদের ডেটল সাবান দিয়ে ওয়াস করলে কখনো ভালো হবেনা। কারন বাংলাদেশ এখন আর আগের মতো সুন্দর পরিবেশ নেই। বাংলাদেশ এখন বিষ কৃট পতক্ষ ভরে গেছে। সরকারি চাকরি জীবি অপরাধ করলে তারা চারা পায় আমরা সাধারণ মানুষ কিছু করলে কোন ক্ষমা নাই । আমরা কি পানিতে ভেসে এসেছি নাকি,0,crime
ভিডিও ও যথার্থ প্রমান থাকার পরও আবার তদন্ত করা হবে,0,crime
ভাই আপনাকে 👠👡👢👟👞 এই গুলো দিয়ে পিটাইতে খুব ইচ্ছা করছে বিশ্বাস করেন,0,crime
এ হল আমাদের দেশে আইনশৃঙ্খলা বাহিনী,0,crime
মিন্নি প্রথমবার বেড় হয়ে কাউকে না দেখে এদিক ওদিক থাকিয়ে দৌড়ে মেরে কলেজ গেটের ভেতরে ঢুকল। পরেবার হলো উল্টোটা বন্ডবাহিনী রিফাতকে ধরে নিয়ে যাচ্ছে আর মিন্নি স্বাভাবিকভাবেই হেটে যাচ্ছে পেছন পেছন পরিকল্পনায় মিন্নি জড়িত ফুটেজ বলছে,0,crime
রিফাতের জন্য সবাই দোয়া করবেন আমিন,0,crime
ডিসি যখন এইটা করছে তখন ভাবছে কেউ বুজি দেখবে না।আর আজ দুনিয়ার সব মানুষই দেখল।হায়রে মিডিয়া,0,crime
খেলা হপে। রুমিন ফারহানার ফ্ল্যাট ইস্যু দিয়া তার সংবাদ গোপন করবে।,0,crime
আইনের সব লোক ধরা পড়ার আগেই সবাই ভালো,0,crime
ফাসি চাই মিন্নি,0,crime
এই কারণে মেয়েদের চাকরি হয়,0,crime
আমি যা দেখলাম রিফাত হত্যায় মেয়েটা ও জড়িত,0,crime
এখানেই বুঝা যাচ্ছে হত্যার মুল কাহিনী তৈরী করেছে মিন্নী শরীফ। তাকে আইনের আওয়াতায় আনা হোক। সব গোমড় ফাঁস হয়ে যাবে।,0,crime
আল্লাহ যে চিতকার বেসি করে তার যেন মরার সময় আযাব বেসি হয় কারন ওকে পুরান পাপে ধরছে,0,crime
যে মেয়েটা তাঁর ছবি দেখাতে চাচ্ছেনা তাকে এভাবে জবরদস্তি করার কারন কি? এতদিন কি করেছিলেন? সাংবাদিকতার কিছু নর্ম আছে যা এইসকল অর্ধশিক্ষিত লোকদের শেখানো উচিৎ।,0,crime
যখন শুরু হলো ফাইটিং তখন নিরবতা পালন করছে স্ত্রী যখন আস্তে আস্তে পুরোটা হিটে চলে গিয়ে রক্তাক্ত জখম হয়েছে তখন মৃত্যু যখন অতি কাছে তখন স্ত্রী স্বামী কে বাঁচানোর চেষ্টা করছে 🤐 বিষয় টা খুব অদ্ভুত মনে হচ্ছে।,0,crime
আমি ছাএলীগ করি তবে এই সব কাজ দেখলে নিজেকে ও গৃন্যা হয় কিসের লীগ লীগ নামে দান্দা বাজি করে কিচু লোকেরা,0,crime
দেশে যদি ইসলাম শাসন থাকত তাহলে ব্যভিচারিণী বাচার কোন উপায় থাকবেনা সারের কোন দোষ নাই সব দোষ কার,0,crime
কি আর বাচবে তুমি তো মরেই গেছো টাকা ভালোই কামাইছো বরকা হিজাব ণেকাব পড়ছোত কেন সব কিছুই ভিডিও তে দেখা যায় যাইতেছে,0,crime
বাংলাদেশে এত লুইচ্চার নষ্টামি প্রকাশ হওয়ার পর ও সাধারণ ভাবে কথা বলে কিভাবে জেলহাজতে প্রেরণ করে তারপর মামলার বিচার কার্যক্রম শুরু হওয়া উচিত । আইনের আজ এই দুরবস্থার হেতু কি ধিক্কার জানাই ।,0,crime
এখানে জোর করে কিছু হয় নি মেয়েটি ইচ্ছে কৃত ভাবেই সব করতেছে মেয়ে টারো দোস আছে,0,crime
আর সাধনা র পুরো সেক্সের ভিডিও টি দেখলাম। এর মানে কি বাংলাদেশের প্রত্যেকটি র জন্য আলাদা সেক্স রুম আছে হায়রে বাংলার কপাল! এই জন্যই তো বাংলাদেশে ধর্ষণের বিচার মাত্র ।,0,crime
অনেক কস্ট লাগলো গানটি সুনে,0,crime
মিন্নি আসলে জড়াজড়ি করে নয়ন বন্ডকে বাচানোর চেষ্টা করছিল। কারন স্বামী রিফাত শরীফ মারা গেলে নয়ন বন্ড হয়ত জেলে যাবে তখন সে মিন্নি নষ্টামি করবে কার সাথে। মিন্নি তোমাকে আসলে প্রধান আসামি করা উচিত ছিল।,0,crime
আরে আপনার মত মহিলা বাঁচার ছেয়ে মরে যাওয়া অনেক ভালো আপনি এখনো কচু গাছে ফাঁসি দিয়ে মরেন নাই আমার মনে হয় আল্লাহ আপনাকে লজ্জা শরম বলতে কিছুই দেয় নাই ছিঃ ছিঃ ছিঃ,0,crime
মিন্নি জড়িত আছে আর এই কারনে বলছি আর এক ভিডিওতে দেখলাম সে পিছন থেকে দুই হাত দিয়ে নয়ন কুকুরটাকে ধরেছিল মিন্নি। আর একটু পিছিয়েছিল নয়ন কুকুরটাকে আর তখন মিন্নির দিকে তাকিয়েছে নয়ন আর তখন এগিয়ে গিয়ে কুপিয়ে মারতেছিল রিফাতকে। তবে আমি নিশ্চিত পুলিশে মিন্নিকে রিমান্ড করলেই সবকিছু বেরিয়ে আসবে সত্যি কথা কারণ পুলিশের ডান্ডা খেলে মানুষ হয় ঠান্ডা ? রাকিআ শাহিন সিলেট,0,crime
তোর আর বলতে হবেনা গ্যদা। ওর ফাসি হোক,0,crime
ভাই আমার মন্তব্য হলো। এর সবাই কে এর সামনে গুলি করে।আথবা কুপিয়ে মেরে পেলা হোক । আপনারা কি বলেন?,0,crime
ওকে ফাসি না দিয়ে একটু একটু করে মারা হক বাংলাদেশ কথা আর কি বলবো,0,crime
ফাঁসির রায় শুনে আমিও খুশি আমার বাড়ি ভারতে,0,crime
ডিসি ধোঁয়া তুলসি পাতা রে দুটোরে মৃত্যুদন্ড দেওয়া উচিত তবে এ দেশে তা হবেনা।,0,crime
আমি এই গ্রুপের সকলের ফাঁসি চাই বিশেষ করে রিফাত ফারাজের ফাঁসি চাই ফাঁসি চাই,0,crime
ওদেরকে তারা তারি ফাঁসি দেওয়া হোক,0,crime
আমার মতে মিন্নি হচ্ছে প্রকৃত অপরাধী কারণ মিন্নি আর রিফাত যে বাইরে ঘুরতে যাবে সেটা নয়ন কিভাবে জানলো? নয়ন যেদিন রিফাতকে হত্যা করবে তার আগের দিন সে তার বন্ধুদেরকে বলে তারা যেনো টার দিকে ঐ কলেজের সামনে থাকে তারমানে নয়ন আগে থেকেই জানতো যে রিফাত ঐ সময় কলেজের দিকে থাকবে আমি মনে করি মিন্নিই নয়নের সাথে পরিকল্পনা করে রিফাতকে সেখানে নিয়ে যায়,0,crime
এখন কেন এইরকম কতরেছে তাদের মা বাবা যখন তাদের কে সন্রাস বানাইছিলা তখন ভাবনি? তুমি যেই ভাবে কান্না করতেছ সেই ভাবে তার মা বাবাও কান্না করছিলো কিন্তু সে ছিলো নিরপরাধ তোদের গুলো অপরাধী‌ এই রকম মা বাবার অবাধ্য সন্তান এর জন্য কেঁদে লাভ কি? মাননীয় প্রধানমন্ত্রিকে সেলুত জানায় কারণ যারা বেপক ভাবে অন্যায় করে তাদের এমন শাস্তি প্রধান করার জন্য,0,crime
আমার বাল হয়বো বালের দেশে লজ্জাবোধ করি আমি বাংলাদেশের নাগরিক পরিচয় দিতে গিয়ে।যে দেশে ধর্ষনের সাজা হয়না সে দেশে আবার নিজ ইচ্ছে রোমান্স করার কিসের আবার সাজা হবে 🤔🤔🤔🤔🤔,0,crime
মুল কালপিট সাধনা । অফিস টাইম বাদে সাধনা বাড়ীতে থাকতো। সেই সময় জেলার মাস্তান বা টেন্ডার বাজ বা রাজনৈতিক লিডারদের সম্মুখীন হতেহতো। তাদের মন রক্ষার্থে ডিসিকে বলি দিল সাধনা ।একটা কথা ভুলে গিয়েছিল ডিসি যে এসব নারীরা কাহাকে ভালবাসতে পারে না ।এদেরকে পতিতা হিসাবে ভেবে নিতেহতো। সাধনার মত যার কোন পিতৃ মাতৃি পরিচয় নেই সামাজিকভাবে যে দুর্বল স্বামী ছাড়া । তাকে কি করে সাহেব বিশ্বাস করল এর আগে কত রাজনৈতিক নেতা মাস্তান বা সন্ত্রাসীদের সাথে দৈহিক মিলন ঘটায়েছে তা কে জানে র নিকট থেকে সাধনা যখন সুবিধা নিচ্ছে তখন তার ভাগতো অন্য কোথাও দিতেই হবে।এটাই বাস্তবতা। এটাই নিয়ম । সেটা কল্পনা করতে পারেনি । সাধনা কে ব্লাকমেইল করেছে ।দুর্ভাগ্য র ।,0,crime
শুধু রিফাত না রিফাত এর মত অনেক মানুষকে এভাবে প্রাণ দিতে হচ্ছে এইসব অন্যায় কারীদের সুষ্ঠু বিচার হয় না,0,crime
হায় রে নাটক।আর কতো এমন নাটক দেখতে হবে আল্লাহ যানে।।।,0,crime
কিছুই বলার নাই,0,crime
অফিসে খাট থাকবে কেন কোন দেশে আজ পর্যন্ত শুনি নাই অফিসে খাট থাকে !,0,crime
গলাকাট,0,crime
কদিন আগে যে এক ম্যাজিস্ট্রেট পার্কে বসা প্রেমিক প্রেমিকা কে ধরে সাজা দিচ্ছিলো ঐ ম্যাজিস্ট্রেট এখন কই🙄😳,0,crime
এখানে সবাই হারে । জিতে কারা ? এটাই প্রশ্ন ।,0,crime
ভাই এ রকম ভিডিও বানানো টিক হয় না কারন এক জন মানুষ দুনিয়া থেকে চলে গেছে তারে লাইয়া ভিডিও বানাবানানো টিক হয় না আমি কার বাল লাগ্ল না লাগ্ল কিন্তু আমার লাগছে না,0,crime
চোর ধরা খাইছে,0,crime
মিন্নি খুনি,0,crime
বয় যদি পাই তা তাহলে পড়া সোনা ছেরে বাড়ি তে থাকতা তোমার কলিজা টা কেজি,0,crime
কিছু করার নাই অপরাধীর সাজা হওয়া উচিত,0,crime
অনেকটা বিরক্তিকর ভিডিও,0,crime
এ ভিডিওটা দেখলে আর দশজন বয় একাজ কোনদিন করবে না ভিডিওটা বেশি বেশি শেয়ার করুন,0,crime
যে ভিডিও করছে তার বিচার চাই😂😂😂😂😂😂😂🥰,0,crime
তোর বাচার কোন অধিকার নাই বাচ্চাদের দোহাই দিবিনা,0,crime
মেয়ের কথা শুনে মনে হয় তার ওই জিনিসটা অভাব ছিল যার জন্য স্যারের কাছে গেছিল তাই স্যারের দোষ নাই মেয়ে বলতেছে,0,crime
না ভাই মিন্নি নিজে প্রথমে দাড়ীয়ে দাড়ীয়ে দেখেছিলো মিন্নি হলো বড় অপরাধী জখন তার সামিকে আদা মরা করে পেলছে তখন সে তাকে বাচাতে গেছে কিন্তু প্রথম থেকে দাড়ীয়ে দাড়ীয়ে দেখছিলো কারন পুরা ভিডিও টা কোন সাংবাদিক প্রচার করে নাই,0,crime
সরকারের দরকার যেখানে মহিলা অফিসার সেখানে মহিলা সব দেয়া উচিত আর যেখানে পুরুষ সেখানে পুরুষ মানুষ দেয়া উচিত কিন্তু সরকার সব সচিব আর মন্ত্রী রা সবাই কি এক ধরনের কের কি এই বুদ্ধি আর মন ভাব আসে না সব অফিসে আর সব যায়গায় মহিলা আর পুরুষ আলাদা করে চাকরি হোক,0,crime
? আমি একজন চুলের নায়িকা কে হাঁটতে দেখলাম। 🥺,0,crime
হায়রে বাংলাদেশের।,0,crime
তাড়াতাড়ি ফাঁসির চাই,0,crime
  এটাই তো এখনার জুগের মেয়েরা বুঝে না যে তাদের সাধিনতার নাম করে লোভ দেখিয়ে মগজ ধোলাই করে ঘর থেকে বের করে কোউসলে সব কিছু লুট করে নিয়ে যাচ্চে। লুচ্চা শিয়ালদের কথা সব সময় মেয়েদের ভালো লাগে আর আমরা ইসলামিক কিছু বললেই তাদের চোখে চিরো শত্রু হয়ে যাই। আরে ভাই লাগাম ছাড়া হলে কে ঠিক থাকে বলেন। মেয়েদের কে ইসলামে কেনো ঘরে থেকে ঘরয়া কাজ করতে বলা হয়েছে খুব প্রয়জন না হলে বাহিরে গিয়ে কাজ করায় নিতি নিরধারন করেছে এবং কঠিন রুলস দিয়েছে একটা ভালো মেয়েও বেটার সংগে থাকলে খারাপ হতে বাদ্ধ হবে আর এখনকার সমাজ এই দিকেই আগাচ্ছে। নারীবাদি ফেমিনিস্টরা মেয়েদের ব্রেন ওয়াস করছে তাদের বানাচ্ছে অঘসিতো পতিতা । এখনকার জুগের মেয়েরা কাজের নামে একটু আরাল হলেই আকাম করে বেরাচ্ছে ঠোকাচ্চে নিজের সামি কে নিজের পরিবারকে। এটা কি কখনো কাম্মো পুরুশ দোস তো আছেই কিন্তু তারের ঠিক করার থেকে নিজের সাবধানতা বড় আসল কথা নিজের নিয়ত খারাপ হলে অপর মানুসের দোস দিয়ে কি লাভ। এই মেয়ের ইচ্চাই ছিলো ওই বেটাকে পটিয়ে চূদা খাওয়া বিনিমতে টাকা নেওয়া। কনো যদি এই বাজে নিয়ত থাকে তবে এই দিকে তাদের আগাতে বা সফল হতে বেশি সময় লাগে না। পুরুশরা এইসব পরিস্তিতিতে বোকা বনে চায়। তাই মাথায় রাখতে হবে কেও না দেখলেও আল্লাহ দেখছেন আর সেটা বাকি সবাইকেও দেখবেন হয়তো এই দুনিয়ায় নাহলে নিচ্ছিতভাবে পরদুনিয়ায়।,0,crime
ফাঁসি কার্যকর কখন হবে ?? এই কথা বলুন আর দেরি কিসের।।,0,crime
ডিসির জন্য সাধনা হারবাল সমাধান,0,crime
স্ত্রীকে রিমান্ডে নিয়ে জিজ্ঞাসাবাদ করলে সব কিছু ঠিক হয়ে যাবে। যেদিন এই ঘটনা হয় সেদিন স্ত্রীর কথা বলার ধরণ দেখে আমার বুঝতে বাকি নেই ।,0,crime
কি আর হবে!,0,crime
সাধনার স্টল হয়ে গেল আনন্দের মহল ।তবে এই শয়তানলীগের জারজ সরকারের কাছে আবেদন না করে এই অবৈধ সরকারের অপসারণ জরুরি ।,0,crime
এতবর কুকর্ম করার পর দেখি তাদের সেলিব্রেটি অনেক বেরে গেলো মনে হচ্ছে একজন ভি আই পি এর ভিডিও ধারন করছেন । এ কয়দিনে তো উচিত ছিল আইন সংগতভাবে তাদের দুজনার বিয়ে পরিয়ে দিয়ে সমাজ থেকে পাপের বিষ কিছুটা রোধ করে দেয়া । আমি বুঝিনা কি আইন বাংলাদেশে ডিসি সাহেবের কুকর্ম লিলা খেলা হলেও এই মেয়েটির জীবন তো সংশয়ে পোরে গেলো এটা ঘৃণিত অপরাধ তার পরেও জীবনের স্বার্থেই ডিসির সাথেই বিয়ে দিয়ে মেয়েটির তো জীবন বাঁচানো আইনের ফরজ নাকি,0,crime
অনেক ভালো লাগছে!!! কারণ রাফি হত্যার বিচার শুরু হয়ে গিয়েছে!!! আবার কান্নাও পাচ্ছে কারণ অনেকের ঘর সংসার ভেঙে তছমছ হয়ে গেলো!!! রাফি মারা গিয়েছে😪😪😪। আমরা সবাই তার জন্য মাগফিরাত কামনা করি!!! আসামিরাও মরবে😍😍😍। আমরা শীগ্রই তাদের ফাসির সংবাদ শুনতে চাই!!! কিন্তু এই অভাগিনী মা বোনেরা জীবনের বাকিটা সময় অসহায় ভাবে জীবন যাপন করবে!!!😪😪😪। তারা তো কোনো দোষ করেনি!!! সব কিছুর জন্য দায়ি ওই নংরা চখের কুলাংগার শয়তান নামমাত্র হুজুর!!! 😡😡😡,0,crime
সত্য ভাই একদম রাইট,0,crime
খুবই সুন্দর,0,crime
আইনের লোকগুলো এতদিন কোথায় ছিলো এতদিন কি তাদের নজরে পরে নাই একটা জিনিস তো আর হুট করে তৈরি হয়না প্রধান সমস্যা হলো তাদের টাকার ভাগ পাই নাই এজন্য অভিযান চালাইছে😫😫😫😫😫😫,0,crime
তোদের ভিডিও দেখে আমার কয়েকদিন ধরে টয়লেট হয়না কি করবো এখন ভাই একটা উপায় দেন,0,crime
পিছনে পিছনে গেলো যে মেয়েটা সেইতো মিন্নি কিন্তু তার জামাইকে কজন মিলে ধরে নিয়ে যাচ্ছে আর সে পিছনে হাটতে হাটতে যাচ্ছে। ব্যাপারটা কেমন যানি ঠেকলো।,0,crime
নারী কি না পারে ডি সি এখন হিরো থেকে জিরো ডুবাই,0,crime
যারা ডিসলাইক দিয়েছে তারা নিশ্চয়ই খুনিদের সমর্থন করে,0,crime
চরিত্রহীন এবং চরিত্রহীনা উভয়েরই বিচার চাই।,0,crime
চুতা দরছে😅😅,0,crime
এই মেয়েটা ঘটনার সাথে জড়িত এদের প্রকাশ্য দিবালোকে গুলি করে মেরে ফেলা উচিত,0,crime
হায়রে আমার সুনার বাংলা বিচার মানবতা আজ তুমি কুথায়,0,crime
ফাঁসি চাই এই কথা গুলো শুনলে পরে হাসি পায় । বাংলাদেশে তো নিয়মিত প্রকাশ্যে অপ্রকাশ্যে এরকম ঘটনা ঘটছে কোনোটা ভাইরাল হচ্ছে কোনটা হচ্ছে না যেগুলো ভাইরাল হচ্ছে সেগুলোর কি বিচার হয়েছে ধরা যাক খাদিজার কথা অথবা রাজিবের কথা অথবা চট্টগ্রামের পুলিশ ইন্সপেক্টরের কথা । নিয়মিত ধর্ষন হচ্ছে সেগুলোর কথা । কেও আমাকে একটা উদাহরণ দিতে পারবেন যে সাজা হয়েছে বা ফাঁসি হয়েছে কার্যকর হয়েছে ।,0,crime
উনি তো রেপ করে নাই সেক্স করসে তাতে প্রব্লেম কই,0,crime
সুন্দরী আপুর চাঁদ মুখ খানা জাতি দেখতে চায়,0,crime
ওসি মোয়াজ্জেমর বিছার হবে না।,0,crime
কি হবে কিছু ই না ছেলে টার জীবন টা ই বি ফলে গেলো মেয়ে টার কারনে ছেলে টার জীবন গেলো,0,crime
লুল,0,crime
কে জরিত আছে আর কে নেই ভিডিওটি ভালোভাবে দেখুন ঘটনা ঘটার একটু আগে সাদা টির্শাট পরা একজন মটর সাইকেল নিয়া কলেজের গেটের দিকে আসে আবার ঘটনা ঘটার পরপরই লোকটা বের হওয়ার সময় একটা পুলিশের সাথে থেমে কিছু কথা বলে। এখানেও কিছু রহস্য থেকে যায়।,0,crime
মিননি রাজনীতির শিকার। ভারত,0,crime
বোকা লোক মাথায় কিছু নাই। ওনি আবার ডিসি!,0,crime
বাংলাদেশর আইন অনুযায়ী তাদেরকে অপরাধী প্রমান করতে পারবে কি যদি উত্তর না হয় তাহলে অপকর্মের আইন পরিবর্তন করে তাদের দৃষ্টান্ত মুলক শাস্তি দেয়া হোক। আমি শুনেছি নারী পুরুষ নিজেদের সম্মতিতে মিলিত হলে এটাকে কোন অপরাধ হিসাবে গন্য করা হয়না আমাদের দেশে।,0,crime
মিন্নি জড়িত আছে এটা হানডেট পারসেন শিওর।,0,crime
মনে হয় ডিসি এই মহিলাকে হুমকি দিছে তাই বলতেছে স্যারের কোনোও দোষ নাই । আমার বাড়ি জামালপুরে সরকারের উচিৎ তাদের দু জনকেই আইনের আওতায় আনা এবং তাদের চাকরি থেকে বরখাস্ত করতে হবে। ভাবতে অবাক লাগে যে কিনা কুকর্মের বিচার করবে দুঃখের বিষয় আজ সেই বিচারকই কুকর্ম করে । ভবিষ্য প্রজন্মের জন্য কি আমরা এটাই উপহার দিবো,0,crime
আসসালামুআলাইকুম ভাই আপনি তো বড় একটা সাংবাদিক হয়েছেন যে ব্যক্তি চুরি ডাকাতি করে খারাপ করে এই ব্যক্তির সমস্যা নাই বলতেছেন কোন ব্যক্তি দেখছে কোন ব্যক্তি ক্যামেরা লাগাইছে ওইটা সমস্যা ভালো বিচারক তবে আপনাকে বলছি যদি আপনার ওয়াইফ বা বোন যদি এসব গুলা করে ঘরের ভিতরে মনে করেন তখন যদি আপনার ছোট ভাই দেখে বা মোবাইল দিয়ে ভিডিও করে আপনাকে দেখায় তো আপনি কি বলবেন আপনার ছোট ভাইয়ের অন্যায় হয়েছে নাকি আপনার বউ যদি বলে এটা অন্যায় না এটার বিচার নাই তাহলে কি ছেড়ে দিবেন ভালো বিচারক আপনারা আমি যেমন বলেছি এমনি করবেন মনে হয় এই হলো আপনাদের বিচার আপনারা মানুষের পায়খানা ও খেতে পারবেন মনেহয় আমি সঠিক রাস্তা দেখানোর জন্য আমাকে গালিও দিতে পারেন জানি আমি তবে আপনাকে আমি গালি দেই নাই রাস্তাটা দেখাইছি কেমন যে গিয়ান আপনাদের মানুষ বুঝে সঠিক কোনটা,0,crime
ভাইরে সাধারণ একটা যুক্তি বুঝছনা মিন্নী যদি ওর স্বামীরে মারতে চাইতো তাহলে এভাবে প্রকাশে মারার কি দরকার ছিলো আর আজকে তোরা যারা রিফাত হত্যার বিচার চাই বিচার চাই কইরা লাফাইয়া চান্দে যাইতাছত তোদের মত মানুষের সামনেই রিফাতরে কুপাইছিলো তোরা কয় আছিলি।এতগুলো মানুষের মধ্যে থেকে দশ মানুষ আগাইয়া গেলেই তো আজ রিফাত থাকতো তোর এই প্রশ্নের উওর দেওয়ার জন্য।পিছনে হেঁটে হেঁটে গেছে এই কারনেই মিন্নি খুনি তোদের মাথায় কি কিছু নাই।আমার মাঝে মাঝে প্রচুর ঘৃণা হয় যে আমি তোদের সাথে বাস করি যত্তসব আবাল বলদের দল।,0,crime
মিনি বলেছে আমার হাজব্যান্ডকে আমি হাসপাতালে নিয়ে গেছি কই মিনিত হাজব্যান্ডকে ফেলে রেখে চলে গেল,0,crime
অপরাধীকে ফাঁসী দিন,0,crime
মনে হয় কিছুক্ষন আগেই খেলা করে আবার আসছে এখন আর খারায় না,0,crime
মানুষ স্পোর্টস ক্লাবে ভাত খেতে আসে এটা হাইস্যকর হাইস্যকর,0,crime
এর নাম প্রথম আলো না হয়ে চির আন্ধকার হওয়া উচিত,0,crime
ভিডিওতে দেখলাম ডিসি সাহেব ভালো করে চুদদে পারে শোনাস সোনা ছামার ভিতরে অল্পেতে ঢুকাইছে এই হল রে ভাই বাংলাদেশের ডিসির অবস্থা,0,crime
ব্যভিচারিণী নারী ব্যভিচারী পুরুষ তাদের প্রত্যেককে একশ করে বেত্রাঘাত কর। আল্লাহর বিধান কার্যকর কারণে তাদের প্রতি যেন তোমাদের মনে দয়ার উদ্রেক না হয় যদি তোমরা আল্লাহর প্রতি ও পরকালের প্রতি বিশ্বাসী হয়ে থাক। মুসলমানদের একটি দল যেন তাদের শাস্তি প্রত্যক্ষ করে। সূরাঃ আন নূর আয়াতঃ ‘আমের ইবনু সা আদ ইবনু আবূ ওয়াক্কাস রহঃ থেকে বর্ণিতঃ তিনি বলেন আমি জাবির ইবনু সামুরাহ্‌ রাঃ এর নিকট আমার গোলাম নাফি র মাধ্যমে চিঠি প্রেরণ করলাম যে আপনি আমাকে এমন কিছু সম্পর্কে অবহিত করুন যা আপনি রসূলুল্লাহ সাল্লাল্লাহু ‘আলাইহি ওয়াসাল্লাম এর নিকট শুনেছেন। রাবী বলেন তিনি আমাকে লিখলেনঃ জুমু আর দিন সন্ধ্যায় যে দিন মায়েজ আসলামীকে রজম ব্যাভিচারজনিত অপরাধের শাস্তি হিসেবে পাথর মেরে হত্যা করা হয় সেদিন আমি রসূলুল্লাহ সাল্লাল্লাহু ‘আলাইহি ওয়াসাল্লাম কে বলতে শুনেছি এ দ্বীন অব্যাহতভাবে প্রতিষ্ঠিত থাকবে যতক্ষণ কিয়ামাত কায়িম হয় অথবা তোমরা বারজন খলীফা কর্তৃক শাসিত হও এঁদের সকলেই হবে কুরায়শ থেকে। আমি তাঁকে আরও বলতে শুনেছি মুসলিমদের একটি ছোট্ট দল জয় করবে শ্বেতভবন যা কিসরা কিংবা কিসরা বংশীয় রাজমহল। আমি আরও বলতে শুনেছি “কিয়ামাতের প্রাক্কালে অনেক মিথ্যাবাদীর আবির্ভাব হবে তোমরা তাদের ব্যাপারে সতর্ক থাকবে।” আমি তাঁকে আরও বলতে শুনেছি “তোমাদের কাউকে যখন আল্লাহ কল্যাণ সম্পদ দান করেন তখন সে নিজের এবং তার পরিবারস্থ লোকজন দ্বারা ব্যয় শুরু করবে।” আমি তাঁকে আরও বলতে শুনেছি “হাওযে কাউসারে আমি তোমাদের অগ্রগামী হবো।” ই ফা ই সে সহিহ মুসলিম হাদিস নং হাদিসের মান সহিহ হাদিস,0,crime
ঠিক ঠিক,0,crime
আমার বাডি জামালপুর ডিসি সাহেবের কিছু হবেনা কারন তিনি প্রধান মন্ত্রীর আত্তীয় ডিসি সাহেব নিজেই বলেছেন শেখহাসিনা তার ভাবী,0,crime
মতিঝিলের মত জায়গায় ক্যাসিনো আছে তা আবার আইন শৃংখলা বাহিনী এতদিন ধরে জানে না এ কেমনে হয় ।কিন্তু আছে,0,crime
এদের কবে ফাসি হবে জানিয়ে দাও।,0,crime
পুলিশ সুপার বলে এরা বিভিন্ন অপরাধের সাথে জরিত তাহলে এদের কেন গ্রেফতার করেনি পুলিশ আগে পুলিশ কে কোপানো উচিৎ,0,crime
তদন্ত ডিসির আব্বা করবে,0,crime
এটা হাস্যকর ছিল। ডিসি বলে কিছুই করেনি। মিনিট কি বসে বসে তোমার চেহারা দেখেছে।,0,crime
তার মানে ঐ মহিলার এখনো চাকরি আছে !! আর ডিসি বেচারার অবস্থা,0,crime
মিন্নি যদি তার স্বামিকে মারতেই চাইত তাহলে কেন কলেজের সামনে আসল।পাকে কেন গেলনা।,0,crime
আমারে কেউ দর হাসতে হাসতে পেন্ট খুলে গেলো রে,0,crime
এই তুই কি সাংবাদিক গাধা,0,crime
ঘটনা ঘটাইছে সে আবার সেই তদন্ত করে দেখবে বাহহহ বাহহহ বাহহ কথা কন না কেরে,0,crime
এদের কি করা যায় আপনাদের মতামত,0,crime
কয়দিন পর দেখবে আর কনো খবর নাই,0,crime
ওইখানকার মানুষদেরকে কি বলবো ভাই বলার ভাষা নাই,0,crime
এরা হাফেজ না কলক ফুতনা বাজ দাজ্জা মুনাফেক ফাঁসি চাই আমরা সিরাজ ফাঁসি নুরুল ফাঁসি সাদাত ফাঁসি,0,crime
তারা বিয়া পারাই দিয়েন,0,crime
সত্যি কথা বলছে এই মহিলা কারণ ডিসি সাহেব তো ওনাকে কোন ক্ষতি করিনি বরং মিনিট ধরে ওনাকে সুখ শান্তি দিয়েছে,0,crime
আহারে ডি ছি ছি,0,crime
এদের মত কয়েকটা মেয়ের জন্য অনেকের সুখের সংসার দুঃখের সাগরে পরিনত হচ্চে,0,crime
এই ইতর ।এক দিন হোক আর সাত দিনে হোক।তাতে কি বদমাইশ সাহেব নির্দোষ ।এই পেচাল না পেরে ধন্যবাদ যে সাহস করে এই জঘন্য কর্মকান্ডে লিপ্ত থাকার মুখোশ উন্মোচন করে দেবার জন্য। কেন গ্রেফতার করা যাবে না এটা কি অপরাধ নয় যদি অপরাধ না হয় তবে কেন এই সব অপকর্মে লিপ্ত নারী পুরুষ কে অতীতে গ্রেফতার করা হয়েছে।তারাতো কেহ অভিযোগ করে নাই।অঅও এটা রাম লীলা কৃষ্ণ লীলা।তাই জায়েজ।তবে তো কে ভিডিও করা র সঙ্গে জড়িত সে মহা অন্যায় করে ফেলেছে ।,0,crime
লাভ নেই ভাই কিছুই হবে না জয় বাংলা,0,crime
ভিডিও দেখে বুজলাম তেমন কিছুই করে নাই! ঈদ পরবর্তী কোলাকুলি করেছে। মুসলমান মাত্রই ঈদের কোলাকুলি করতেই পারে।,0,crime
বাঙালীর গর্ব🐸🤣,0,crime
একটা ভিডিও ক্লিপ ও দেখলাম না তার আবেগি মন নিয়ে স্বামী হত্যার বিচার চাইতে কান্না জর্জরিত হয়ে ভেঙে পড়তে স্বাভাবিকভাবে সাক্ষাৎকার দিয়েছে টিভিতে তাকে সব বেরিয়ে আসবে এধরনের কিছু মেয়েদের জন্য মারামারি হয় আমাদের দেশে,0,crime
গানটা খুব সুন্দর গেয়েছেন সুন্দর করে গাওয়ার জন্য দ্বায়ী হল ঐ লোকটার বউ।কারন ওকে দেখে আপনার সুরটা অনেক মধুর হল।সাবাস সাবাস🤣😂🤣😂,0,crime
? থেকে ? কই!!! কাহিনী তো এখানেই,0,crime
তদন্তে এটা আসতে পারে ডিসি সাহেব সব কিছু সরল মনে করছে। দেখা যাক কি হয় তদন্ত হোক।,0,crime
মিন্নিকে দরে নিয়ে রিমান্ডে নেন সব বের হবে,0,crime
এই জারি টা আপনাগো করা হয়না রাগ করবেনা ভাই এই নাটক দেখ আর খারাপ হলো মেয়েরা এগুলো বাদ দিয়ে জেটা সত্য এটা করেন।ওকে,0,crime
ডাইরেক ফা্ঁসি চাই,0,crime
স্যারের দুই মিনিটের কাজে এতো মজেছেন স্যার এর কোন দুষ নাই সন্তানের জন্য বেঁচে আছি আর কতো ঢপের কিত্তন আর দিস না,0,crime
বাংলা সিনেমার মতো মারামারির পর পুলিশ মামা আইসা হাজির,0,crime
রিফাত হত্যার দায় কার?? আজকে আমাদের মা বাবা মেয়েদের পর্দা ছাড়া ছাড়া ছেড়ে দেয়। ফলে মেয়ে নোংরা সম্পর্কে জড়িয়ে পড়ে মা বাবা উপায় না দেখে বিয়ে দিয়ে দেয় ছেলেদের বলছিঃ বিয়ে করার আগে মেয়ের চরিত্র দেখো। সমাজে নোংরা সম্পর্ককে পবিত্র সম্পর্ক বলে প্রচার করা হচ্ছে। ঘরে ঘরে অশ্লীল টিভি চ্যানেল স্থান করে নিয়েছে।তাহলে এ দায় কার!! মেয়েদের বলছিঃ আল্লাহতো তোমাকে তোমার বরের জন্য সৃষ্টি করেছেন।তাহলে কেন তুমি তোমার সৌন্দর্য অন্যকে দেখাবে?? আসুন আমরা ইসলামের নৈতিক বিধিনিষেধ মেনে চলি।সুন্দর সুস্থ সমাজ গড়ি,0,crime
ভাই ওরে বলেন দিতে এটা দেখতে একটু সমস্যা হয়,0,crime
অনেক ভালো লাগলো। বন্ধুরা আমার চ্যানেলটা সাবস্ক্রাইব করুন লাইক দিন এবং কমেন্ট করুন,0,crime
রানা ভাই আপনার এতো মর্মান্তিক হৃদয় বিদারক অভিনয় দেখে আমরা মুগ্ধ। আশা করি আপনি আমাদের আরো সুন্দর সুন্দর ভিডিও উপহার দিবেন । ধন্যবাদ,0,crime
বিশ্বাস করেন এদের কান্না দেখে মন খুলে হাসতেছি খুব ভালো লাগলো তোদের কান্না দেখে পরের মেয়েকে যখন এভাবে মারলো তখন তার মাও তো কান্না করছিলো তখন কই ছিলি তোরা????,0,crime
ঠিক।বলছেন,0,crime
এই খানে খুব ভালো ভাবে বুঝা যাচ্ছে যে এই ঘটনা মূল অপরাধী মিন্নি কারণ খুনিদের মধ্যে কোন মানুষ মিন্নির শরীলে হাত দায় নী বা তার গাঁয়ে একটা ও ফুলের টুকাও পরেনী মিন্নি আসল অপরাধী,0,crime
একেবারে ঠিক করছে সবার জন্য ঠিক আছে বিচার।,0,crime
অসাধারণ আমার প্রিয়গান,0,crime
হাহাহা।।।।।।।। এটা নাকি সাজানো।,0,crime
এটা না কি হেকারদের কাই কারবার তাও আবার আমাদের মানতে হবে এটা হাসি তামাস্যা ছারা আরকি মনে হয়,0,crime
আমি ও অপরাধীর সাজা চাই কিন্তু কিছু মানুষকে বলতে চাই আসামীর স্বজন দের যারা গালিদিতেছেন এই গালিদিবেন না কারণ তারা আসামী কে বলে দেয় নাই নুসরাতকে হত্যা করতে। অপরাধ যে করেছে সাজা সে পাবে এবং আমরা তার সাজা কামনা করি। কাজে আমরা সবাই আসামীর বিচার কার্য আদালত সুন্দর ভাবে দৃষ্ঠান্ত রাখতে পারে এই দোয়া করি।,0,crime
এমন মানুষ কোনো করে,0,crime
এই মেয়ে কে সেফুদার এক টা ডায়লগ দিয়ে জান সবায়,0,crime
হাইরে নিষ্টর মানুষ,0,crime
ডিসির অকেজো মেশিনের এত্ত জোর!! প্রেগন্যান্ট করে দিছে!!,0,crime
এই ঘটনা মিন্নি ঘটিয়েছে,0,crime
ঠিক ঠিক বলেছেন টিপু সুলতান ভাইয়া !!,0,crime
জামালপুরের ডি সি সাহেবের অপমানের জন্য সি সি ক্যামেরার ফাঁসি চাই।,0,crime
কী এক অদ্ভুত কান্ড নিজে আকাম করল আবার নিজের তদন্ত করবে জিনিসটা হাস্যকর হাস্যকর,0,crime
বিচার চাই জনের,0,crime
ওদেরকে জলদি ফাঁসি চাই,0,crime
ফাঁসি চাই,0,crime
এই সব কাপুরুষ দের জন্য মানুষ লেখা পড়া করে না পড়া লেখা করে চাকরির জন্য যখন টাকা না হলে দেহোবুক,0,crime
জামালপুরের ডিসি ফাঁসি চাই।।। আমার এই কথার সাথে কি আপনি একমত,0,crime
ডিসি তর খেলা আমি দেকছি তুই পারছ না খেলতে তর ভউ অন্য বেটাগো লগে খেইল লয় সিওর,0,crime
মিন্নিও যে সাথে জড়িত এতে সন্দেহ নেই,0,crime
দেশের মানুষ কি পাগল হয়ে গেলো নাকি মিনিট খেলার পরেও বলে কিছু জানেনা,0,crime
ছি ছি ছি লজ্জা হয়,0,crime
মিন্নি ভালোই অভিনয় করে দেখছি,0,crime
খুব খারাপ লাগছে ছেলেটা মৃত্যু তে।আমার কথা আশেপাশে কি কোনো মানুষ ছিল না?আজ যদি কিছু মানুষ এগিয়ে আসতো তাকে এত কঠোর ভাবে মরতে হতো।সবার কে বলি।আপনারা একজনের বিপদে এগিয়ে আসুন মানুষ তো মানুষের জন্য।,0,crime
এদের সামনে আসামি গুলাকে আগুন দিয়া মারলে ভালো হইতো কত নির্মম ভাবে জিবিত মেয়েটা কে আগুন দিয়া হত্যা করলো।,0,crime
দেখ মরন জালা কেমন জালা,0,crime
সুতানে দল নামায পর বালে গান,0,crime
ঠিক বলাছেন ভাই,0,crime
এরে ফাঁসি দেয়া হউক,0,crime
সবত বি ডি ও তে দেখাগেল আবার কিসের তদন্ত গুস খাওয়ার ধানদা,0,crime
ফাসি দে,0,crime
এদের কঠিন বিচার করতে হবে,0,crime
আপনাদের কাছে আমার অনুরোধ ঐ মেয়ের শশুর বাড়ী সব কিছু বলেদেবেন কারন আর কারও বৌ এমন কাজ না করতে পারে আবার ওরা নাকি জাতির মা চিছিছিছিছ,0,crime
যারা যারা এর সাথে জরিত আছে তাদের কে পাশি দেযার জন্য আপনাদেরকে বলছি আমার বাড়ি কুমিললা,0,crime
মিননির হাত আছে আমার মনে হয় না। কারন ওদের বিয়ে হয়েছে মাত্র দুইমাস।,0,crime
ডিসি বনাম পিএসএর মিনিটের ম্যাচ লিংক 😁😁,0,crime
সব গুলোকেই ক্রস ফায়ার দিতে হবে,0,crime
বলুন তো ভায় এত একন মঙ্গল আছে একটা মেয়ে কে এমনভাএব নাজেহাল করে?? যে দেশে চাকরি নেই সম্মান্নেই বেচে থাকবার কোন পরিবেশ নেই। চিহ।এক্তা মেয়েকে রেহাই দিন,0,crime
কঠিন বিচার বিভাগের কাছেই সাসতি চাঠ,0,crime
এই মেয়েটাই নাটের গুরু,0,crime
কান্না করে লাব নাই দেশে অপরাধীর বিচার হবে তাদের ফাসি তারা তারি হোক,0,crime
বিচার যাইহোক। তালগাছ আমার,0,crime
নুসরাতের মত ওদের কেও পুরিয়ে মারার দরকার ছিল,0,crime
আপনারা ঠিক বলেছেন আমাদের প্রতিবাদ করতে হবে বসে থেক। লাভ। হবে না,0,crime
ভারতের মতো এদেশে ও দ্রুত সাজার আইন না করলে এমন অপরাধ বার বার হবে।,0,crime
ভোলার হ্যাকারদের ফাঁসির আদেশ হোক ।,0,crime
আললায় নিষচয় বিচার করবেন পাপ বাপ কেও ছারেনা,0,crime
নিজ চোখে দেখে তারপর তদন্তের কীসের দরকার রককক সমাজৈর ভক্ষক,0,crime
পুলিশ সোনা পাখি,0,crime
এই সমস্ত বিপদে যে পুরুষ আগায় না আসে ও পুরুষ না অন্য কিছু ওকে নিন্দা জানাই এ সমস্ত পুরুষকে,0,crime
এখনো মেনে নিতে পারতেছিনা যখন ফাঁসি হবে তখন বুজবো যে আমাদের দেশে আইন আছে,0,crime
দারুন হয়েচে,0,crime
তদন্ত নামের জারজ কথাটি আমাদের দেশে প্রচলিত হাস্সকর।,0,crime
অনেক ভাল লাগল ভাই আপনার কথাগুলি,0,crime
মিন্নি তো ওদের সাথেই হাটি ঐ খানে গেলো তার মানে হিতি মূল অপরাধী হিতিরে ওহ দরা হোক।,0,crime
এই ভিডিও দেখে প্রমাণিত হয় মিন্নি জড়িত কারণ তার স্বামীকে অরা মেরে মেরে নিয়ে যাচ্ছে আর মিন্নি নিরবে হাটছে,0,crime
এই সব কুক্ষাত শয়তানকে ফাসির আওতায় আনা হলে দেশ ও জনগন শিক্ষা পাবে যাতে আর এমন ঘটনা না ঘটে। আমি জোরদার দাবি করছি।,0,crime
স্যারের কোনো দোষ নাই ম্যাডামেরও কোনো দোষ নাই। সব দোষ চি চি ক্যামেরার 😄। স্যারের যন্ত্রটা একটু বেশি গরম হয়ে গেছিলো আর উনি শুধু যন্তটার উপরে ওঠে পকাত পকাত করে ওঠাকে ঠাণ্ডা করেছিলেন। 😂,0,crime
উনি ভুল করেছেন কিন্তু এটা চক্রান্ত। তদন্ত করলে বেরিয়ে আসবে,0,crime
জিনিসটা আসলেই হাস্যকর কে কাকে বলবে ফকিন্নি দেশের ফকিন্নি লোক,0,crime
যারা বল্লো বিজলির কারনে সি সি কেমের‍্যারা খারাপ হয়েগিয়েছে তাদের কি হবে আইনের গতিতে আমরা দেখতে চাই যারা একমত আছেন তারা সারাদেন,0,crime
অবিলম্বে মিন্নিকে গ্রেফতার করা হোক। এই হত্যার সাথে মিন্নি জড়িত স্পষ্ট বুঝা যাচ্ছে। মিন্নি যথেস্ট নাটক করেছে। এই নাটকের শেষ হওয়া দরকার।,0,crime
যে আপলোড দিছে তার বুকের পাটা আছে এইটা মানতে হবে ।,0,crime
এত সুন্দর একটা ভিডিও দেখার পরেও মানুষ ভাববে এটা সরযন্ত্র ইতিহাসে এরকমের সাদু সন্যাশী হাতেনাতে অনেক ধরা পরেছে আজকাল মানুষ আর ছাগল নয় মানুষ সবই বোঝে ।,0,crime
পাসি দেয়া উচিত,0,crime
ভাই এত মজা করিবেননা।দুদিন পর দেখবেন তথ্যবাবাড তথ্যে বেরিয়ে আসবে ডিসি সাহেব ছাত্র জীবনে শিবির বা ছাত্রদলের নেতা ছিলেন তথ্য বাবার আম্মগু অনেক মেজিক জানেন মনে নেই কি বালিশ দুর্ণীতিবাজ ছাত্রদলের নেতা হয়েছিলেন শেষ মূহুর্তে।একটু অপেক্ষা করুন।,0,crime
ইনাকে চাকরি থেকে বহিশকার হোক,0,crime
ঠিকি বলেছেন ভাই যদি এই ডিসির দাড়ি টুপি থাকতো তালে নারীবাদিদের শোকের ছায়া পড়ে যেত মু্ন্নি শাহ মাসুদা ভট্টি শয়তান কবির মতো নারীবাদিরা আজ কোথায়,0,crime
অনেক আগ থেকে চলা সত্তেও এত্তোদিন পর কেন এদের দরা হ প্রশাসন জানবে না কেনো এতো বড় একটা ক্লাব এখানে এতোদিন দরে ছলতেছে।। ভাগের টাকা ঠিক মতো না পাওয়ায় এই অভিজান আমার মনে হয়,0,crime
আসলে মিন্নির এরকম ভাবা পিছনে হাটা টা সন্দেহ জনক কিন্তু পিছনে আস্তে আস্তে হেটে গেছে বলেই প্রমাণ হয়না যে মিন্নি এর সাথে জরিত মিন্নি যদি এর সাথে জরিত থাকত তাহলে অবস্যই এর অন্য কোন প্রমাণ থাকত তাছাড়া রিফাত ফরাজি একনো মুখ খুলে বলতে পারতো মিন্নিও এর সাথে জরিত যাদেরকে রিমান্ডে নেওয়া হয়েছে তারাওতো মিন্নির কথা কিছু বলেনি রিফাতের বাবা মাও তাদের বউমাকে কিছু বলেনি তাহলে আমরা কি বুঝব প্রমাণ সরুপ শুধু নয়নের সাথে দুইটা ছবি আরত কিছুই নেই মিন্নি তার সামিকে এইভাবে মারাবে আর নয়ন এরকোন প্রমাণ রাখেনি আসলেই অবিসাশ্ব,0,crime
ত্রকটি সুন্দর রায় দিয়েছেন বাংলাদেশ সরকার আমরা সকল ত্রস্তরের জন গন খুসি দুরুতো বেগে রায় কার জোকর করা হোক,0,crime
আমি শুধু মিন্নির ফাসি চাই দেশ বাশির কাছে,0,crime
এই খুনের পেছনে তার স্ত্রীর ষড়যন্ত্র আছে তাই তাকে দ্রুত এরেস্ট করা হোক বুঝতে পারছি না কেন তাকে রেস করা হচ্ছে না এবং তার মোবাইল নিয়ে চেক করে সব কিছু তথ্য প্রকাশ হবে কারণ সে এখন নাটক করছে এটা তার শুধু অভিনয় তাকে রিমান্ডে নিয়ে জিজ্ঞাসাবাদ করা হোক,0,crime
খুব তাড়াতাড়ি রায় কার্যকর করা হোক এইটাই দাবি,0,crime
এই সরকারের সময় যৌনহয়রানী নারী ধর্ষণ খুন ঘুম কোন বেয়াপার না সব কিছু হালাল,0,crime
আগে আল্লা ছিনলে না এখন ছিনে কি ভাল,0,crime
সাবাস রেব বাহিনী কে ।এক দিন আপনারা সেনাবাহিনীর কে ও ছারিয়ে যাবেন ।,0,crime
সনের আগে থেকেও এই ক্নাব চলছে কিন্তু দিন দিন এতটা বেপরোয়া হয়ে আসছে প্রসাসন আগে থেকে নজর দেওয়া উচিৎ ছিল সরকার যেই হোক ৷,0,crime
আরে বেটা তুই কি ভাবস আমরা ঘাস খাই চোর কখনো চুরি করে কয় যে চুরি করছে তুই এতো রিসার্চ করাতস কে ডিশির হইয়া অইসব আগর বাগর তর বাচ্চারে গিয়ে বুঝা।।,0,crime
অসাধারণ একটা কিস্ছা খুব ভালো লাগলো।,0,crime
জরিত এই মেয়ে টা আমার মনে হয়,0,crime
সঠিক এ খুনে মিন্নি জড়িত ছিলেন। ভিডিও দেখে বুঝা যায় এই খুনের সাথে মিন্নি সরাসরি জরিত।,0,crime
আফসোস লাগে মা বোনদের জন্য কিন্তু কি করবে যেমন কর্ম তেমন ফল,0,crime
তুমি বোন নুসরাতের কান্না যখন শুনতে পাওনাই।আজ তোমার কান্না ও কেহু শুনবে না।আমি এটাই মনে করি।,0,crime
অবৈধ সরকার হাসিনো ঢাকা শহরেটা বানাই ফালাইছে ক্যাসিনো বাংলাদেশ সিঙ্গাপুর হয়ে গেছে উন্নতির জোয়ারে ভাসছে হাইরে হাসিনো দেশটারে বানাইলো ক্যাসিনো কেন আর কত কি দেখাবি তুই এখন নাটক করো বাস এসবকিছু তুমি তোমার পুলিশ রা জানে না তোমার দলের লোকেরা এসব করতেছে ভালোই নাটক জানো হাসিনো দেশকে বানাইলা ক্যাসিনো,0,crime
তার চোরের মতো চেহারাই বলে সেই অপরাধী । সে মামলা করলো না কেণ তার মানে সেই আপরাধী,0,crime
এখানে অনেকে ডিসির স্ত্রীর প্রতিক্রিয়া জানতে চাইছেন তাইনা আমি বলবো এই জন্য বেশির ভাগ স্ত্রীরিরাই দায়ি কারণ তাদের প্রয়োজন মিটাইবার জন্য বিলাসবহুল জীবন যাপনের জন্য গাড়ী বাড়ি সোনা গহনা ইত্যাদি তাদের চাই চাই কি ফোটানিরে বাবা এদিক দিয়ে স্বামি বেচারা অপরাদ করতে করতে কলিজা বড় হয়েই যায় তখন আর অপরাধ অপরাধ মনে হয়না। ফেরআওনের স্ত্রী আছিয়া পৃথিবীতে কমিই জন্ম নেয়। হয়ত আমার ধারনা ভুল হতে পারে। আল্লাহ আলম।,0,crime
কতটুকুন অনৈতিকতা হয়েছে সেটা তো ভিডিও দেখেই বোজা যাচ্ছে এখানে তো ডিসি সাহেব কে জোর জবরদস্তি করা হইতেছে না ঐ নারি কে চুমা দেওয়ার জন্য জড়িয়ে বুকের ভিতরে নেওয়ার জন্য পুরা ভিডিও দেখেই বোজা যাইতেছে কত আপশে এই কাজ করলেন ডিসি সাহেব,0,crime
আসসালামু আলাইকুম যদি কোন সরকারি কর্মকর্তা বড় অফিসার নারী কেলেঙ্কারি হোক ইয়াবা পাচার তারা সরকারি চাকরি করে বলে অনায়াসে পার পেয়ে যায় এটা সুনিদৃষ্ট আইনের লংঘন আমাদের প্রধানমন্ত্রী প্রেসিডেন্ট আরো অন্যান্য নেতারা জোর গলায় বক্তৃতা দেন আইন সবার জন্য সমান মিথ্যা বক্তব্য দেয়া কবে শেষ হবে তাহলে সাধারণ মানুষের জন্য তৎক্ষণাৎ ব্যবস্থা আর সরকারি কর্ম কুত্তা হলে এই ইনকোয়ারি সেই ইনকোয়ারি দেখছি প্রমাণ হোক দেখা যাবে না না ফন্দিফিকির চালু হয় আমাদের সরকারকে এমন আইন করতে হবে তাৎক্ষণাৎ বরখাস্ত সে যেই হোক আমাদের সরকার ঘুষখোর চাঁদাবাজ পুলিশ নামের যারা সন্তান এদেরকে সাপোর্ট করে যাচ্ছে স্পষ্ট,0,crime
সোনার ময়না পাখি যতই বাঁচার চেষ্টা করো বাঁচার উপায় নাই জনগণ এত বোকা না,0,crime
ব্যাপার না আওয়ামী লীগ আছে আছে না।সব ঠিক করে নিবে।,0,crime
পরিবেশটা খুব সুন্দর না কোন হৈচৈ আছে সাধনা কি কাউকে গালি দিয়েছে কাহারো বিরুদ্ধে বলতেছে তারপরও সবাই বলি সাধনা ভালা না ভালা লইয়া থাইকো তোর কপালে জুতার বাড়ি হারামি দেহ দিলা মন দিলা না মন দিলা দেহ দিলানা।,0,crime
আওয়ামীলীগ করলে সাত গুন মাফ আল্লাহ কবে যে এই পাপ থেকে ঈমান দার মানুষকে মুক্ত করবেন,0,crime
শুধু এটুকুই ভাবছি তার সন্তানেরা যখন এটা দেখতে পারবে ভবিষ্যতে তখন নিজের মাকে নিয়ে কি চিন্তা করতে পারে। স ্পিচলেস 😨।,0,crime
মিন্নির হাঁটা চলা দেখলে বুঝা য়ায় যে ঐ মেয়ের ষড়যন্ত্রে রিফাত কে ধরে নেওয়া হয়েছে।কারণ হচ্ছে যদি রিফাতকে হঠাৎ করে ধরত তাহলে মেয়েটি আতঙ্কে থাকতো। এখানে মেয়েটিকে আতঙ্কের কিছুই বোঝা যায় না । আমার মনে হচ্ছে মিন্নি নয়নবন্ড এবং রিফাতদের সহযোগী। মিন্নির ডি এন এ টেস্ট করা হোক আমাদের মনে হচ্ছে ওই মেয়ে ও মাদকে আসক্ত। উর্দ্ধতন কর্মকর্তার প্রতি আকুল অনুরোধ যে এই ব্যাপারটা ভালো করে তদন্ত করা হোক।এই ভিডিও ফুটেজটি ভালো করে দেখে তদন্ত করা হোক। খুনিদের ফাঁসি হোক।,0,crime
নাটক করে লাভ নেই মিন্নি সত্যটা অনেকটাই সবার সামনে চলে এসেছে সুধু সময়ের অপেক্ষা তোর ও শাস্তি পেতে হবে,0,crime
এই বদমাইশ গুলুরে তারা তারি ফাঁসি দেওয়া হক আমার মনে হয় ঠিক বিচার হয়েছে এমন বিচার হলে দেশে কিছু বদমাইশী কমে।,0,crime
আমি বলি জে সম্পূর্ণ ভাবে মিন্নি জরিত আছে কারন যখন রিফাতকে ধরে নিয়া যায় তখন মিন্নি সাভাবিক ছিল ও যখন রিফতকে কুপিয়ে যায় তখন মিন্নি তার জুতা ঠিক করে চলে যায়। আমার কথা হল যে যখন রিফাতকে ধরে নিয়া গেল তখন মিন্নি কিছু করতে পারতো কিন্তু সে কিছুই করেনি তখন সে পুলিশ কে ফোন করতে পারতো কিন্তু সে সম্পূণ ভাবে সভাবিক ছিল এতে বুঝাযায় মিন্নি জরিত আমি চাই প্রধান মন্ত্রি এই ভিডিও টা দেখে সঠিক অপরাধিকে স্থিতি দেওয়া হক,0,crime
এসব নারীরা জাতির কলঙ্ক! ভাবতে ও অবাক লাগে দোষ করেও স্বীকার করতেছে না! কেউ অাজেবাজে গালি দিয়ে ছোট হবেন না!💓,0,crime
ফ্রী খাওয়াইয়া বিজ্ঞাপন দেই 😂😂😂😂😂,0,crime
দশ দিন চোরি করলে এক দিন ধরা পরবেই। এই ভিডিও তে দেখা যায় নীজের ইচ্ছায় দুজনই অন্তরংগ অবস্তা। ভিডি টি দেখে শ্পট বোঝায় এইটি কোন পরিক্লপিত সরযন্ত নয়,0,crime
এই আর নতুন কি রাজনৈতিক নেতার ই এগুলা করে বেড়ায় এই হালার কপাল খারাপ যে সি সি টিভিতে ভাইরাল হইয়া গেসে!😂😂,0,crime
মুন্নি নিষ্পাপ নয় । স্বামী খুন হতে চলছে এটা না জানলেও তাকে একটু কিল ঘুষি চড় থাপ্পর মারা হবে অথবা ভয় দেখানো হবে যা এই মহিলা জানত বলেই মনে হচ্ছে ।,0,crime
হায়রে বাংলাদেশের মানুষ একটা ছেলে কে এই ভাবে মারলো কোপাইলো কেউ একটু পাশে গেলো না উলটা পালাইলো,0,crime
বাংলাদেশের অাইনের ধারা মোতাবেক উক্ত সিসি ক্যামেরাকে দুইমাস হোয়াইট হাউসে নির্বাসনে পাঠানো হোক।যেহেতু ও জড় পদার্থের বিচার দাবি করছে।,0,crime
তমো মিনিট কেটে দেওয়া হল কেন??? পরে দেখেচি তমো মিনিটে মিন্নি রিফাতের সাথে জেতে চাইনাই,0,crime
এই মেয়ে হয়তো আগে থেকে সব জানতো এই মেয়ে নিশ্চিত এই ঘটনার সাথে জড়িত যা ফুটেজ দেখে ক্লিয়ার বুঝা যাচ্ছে এটা পরিকল্পিত এই মেয়েকে ও ফাঁশি দেওয়া হোক।,0,crime
চেহারায় বলে দেয় কামলা একটা জুতা মেরে বিতারিত করা হোক জামালপুর জেলা থেকে৷,0,crime
অপরাধ করেছে অপরাধী রা আর কষ্ট পাচ্ছে বাবা মা। পাওয়া টা সাভাবিক তার পর ও শাস্তি তো পেতেই হবে,0,crime
মঝা দুইজনে করছো আর সাস্থি ও দুইজনে পেতে হবে স্যারের দুশ নাই বলতে লজ্জা লাগেনা,0,crime
আরে দেশে বিচার নাই এই জাগা যদি হুজুর থাকতো তাহলে সারা বাংলাদেশে হয় চই সুরু হয় জেতো,0,crime
মিন্নিকে জিগ্গাসা করা হোক।জর্মদিন পালন করেছে কখন কত তারিখে,0,crime
ছি বাজ্ঞালি জাতি ছি।।।।এরা তো এমন ছিল না যারা কথায় কথায় প্রতিবাদ করতো আজ তারা শুধু নিঃশব্দে দেখে গেল।।এত ব্যস্ততম রোডে কাউকে এত নির্মম ভাবে জীবন দিতে হল আর সবাই দর্শক হয়ে তাকিয়ে রইলো!!!!! কেউ এগিয়ে আসেনি!!!!! বাকি অপরাধির ফাসি চাই।।,0,crime
ঐখানে দাঁড়িয়ে থাকা মানুষগুলোর গালে জুতা পেটা করা উচিৎ। ওরা কি ভাত খায়না? নাকি গু খায়। একটা মানুষকে এইভাবে কেলানো হচ্ছে কোপানো হচ্ছে। আর ওরা তাকিয়ে তাকিয়ে মজা নিচ্ছে। ছি। এই আমরা নিজেদের বাঙালি বলে বড়াই করি। ওরা জন পুরুষ এগিয়ে আসলেই নয়ন বন্ড এই সাহসটা পেতোনা। অথবা ওরা পুলিশকে জানাতো তাওতো রিফাত শরিফের প্রাণ বেচে যেতো।,0,crime
মিন্নি বড় আসামি,0,crime
সবাই কি তাকে মেরেছে নাকি একজনকে মারতে কয়জন লাগে সবাই কি ফাঁশির যুগ্য অপরাধী?,0,crime
এসব দেখে মানুষ কেমনে চুপ রইলো আহারে রিফাতের কত যে কষ্ট হয়ে ছিলো,0,crime
এই ছিল বুঝি আমাদের স্বাধীনতার উদ্দেশ্য 😭 আজ আমাদের প্রত্যেকের ন্যায় নিষ্ঠতা এবং বীর পুরুষ ত্বকে নষ্ট ও ধ্বংস করে দিয়েছে ক্ষমতাসীনদের গুম খুন হত্যা আর হামলা মামলার মাধ্যমে !!!!🤐,0,crime
মিন্নী তুমি নাটেরগুরু,0,crime
উনার আসলে কোন দোষ নাই। পরিবেশটা ছিল সুন্দর। কোথাও কোন হইচই ছিলনা। তাই তিনি একটু ঢেলে দিছেন। উনি কাউকে গালিও দেয়নি। তারপরও একদল লোক বলে উনি ভালা না। এখন ডিসি বলে আমিতো ভালা না ভালা লইয়া থাইকো। কথা কি কিলিয়ার না ভেজাল আছে,0,crime
স্যার ত আপনাকে সুখ দিয়েছে তিনি কি ক্ষতি করেছে আপনাকে,0,crime
শয়তান হাত নামিয়ে কথা বল,0,crime
স্টোরি ড্রেসাপ একদম মুল কাহিনীর সাথে ম্যাচিং।। ভালো লাগলো!,0,crime
তুই মর ছি লজা নাই কথা বলে,0,crime
মিন্নি সহ সবাই কে ফাঁসি তে ঝোলানো হোক,0,crime
এত গুলো লোক দেখে তামাশা করল,0,crime
আমি আজো খুসি হয়নি খুসি হবো সে দিন যে দিন আবরারের খুনিদের হাসি হবে,0,crime
এই ভিডিও টা যে ছেড়েছেন তার উচিত হয় নি এভাবে ছাড়া,0,crime
মিন্নি খুন করাতে যাবে কেন মিন্নি চাইলে নয়নের সাথে কবেই বেগে চলে যাইতে পারতো। মিন্নিকে নয়ন উত্তক্ত করতো তাই রিফাত নয়নকে কিছু হয়তো বলেছে পরে নয়ন পরিক্লপনা করে রিফাতকে কুপাইছে হুম তা ঠিক যে মিন্নির সাথে নয়নের আগে হয়তো কোন রিলেশন ছিলো পরে হয়তো তা ব্রেকআপ হয়ে গেছে অত পর রিফাতের সাথে বিয়ে!!! আর এখন আপনারা মেয়েকে দোষ দিচ্ছেন।,0,crime
এক দম ঠিক কথা।,0,crime
এটা শুধু আমার একার দাবি নয় সারা বাংলাদেশের🇧🇩🇧🇩 মা বাবা ভাই বোন এবং সকল নাগরীক দের দাবি।,0,crime
ভাইয়া আপনার বাড়ি কি জামালপুরেই,0,crime
আমার মতে প্রতিটি উপরস্থ সরকারি অফিসারের পারসোনাল রুমে সিসি ক্যামেরা ব্যবহার করা উচিৎ। তাহলে আর এসব করার সাহস পাবে না।যত বড় অফিসার ই হোক না কেনো কোনো বেড রুম থাকবে না।কাজের জন্য টাকা নেয় তারা অফিসে এসে পতিতাদের সাথে নোংরামি করার জন্য না।,0,crime
ভাই কেউ খারাপ গালা গালি না করে বুঝিয়ে বলেন মা বাবা সবার আছে,0,crime
এ জাতি একদিন যুদ্ধ করেছে ভাবলে অবাক লাগে।যত লোক চারপাশে ছিল সবাই একমুঠো করে ধুলাবালি ওদের চোখে মারলে ও ওরা ধুলায় মিশে যেত ।তারপর ওদের দা দিয়ে ওদেরকেই কুটিকুটি করতে হতো।হায়রে পুরুষ পারো শুষু নারীদের অত্যাচার করতে।,0,crime
হা হা হা মিনিট ভাইরাল হোয়ার আগেই মিনিট ডাউনলোড করে ফেলেছি 🤣🤣,0,crime
মিন্নির দুসি,0,crime
এক কথায় ফাসি চাই দেশে কি আইন নাই নাকি এটা কি একটা স্বাধীন দেশ নাকি পরাধীন একটি দেশ,0,crime
সালামুআলাইকুম বনি আমিন ভাই যে কথাগুলি বলেন সবগুলো সঠিক মনে হচ্ছে কোন বাংলাদেশের প্রশাসন এরকম হলে শাসন কি রকম হবে,0,crime
মিন্নি পুরাপুরি বাবে জরিত দেখেন জখন ওকে দরে নিয়ে যায় তখন মিন্নি এদিক ওদিক চায়,0,crime
চুরি তো চুরি আরো শিনাজুড়ি,0,crime
পুলিশ রা তো ঘুষ খাইতো পুলিশ আর মেধর একই রকম হয়ে গেছে বাংলাদেশের,0,crime
এরকম সৎ সাহস নিয়ে সত্য ঘটনা প্রকাশ করার জন্য ধন্যবাদ এর সাথে যারা জড়িত সকলকে ধন্যবাদ,0,crime
অসাধারণ গাইছেন ডিসি সাহেব,0,crime
আল্লাহ জানে বাকিটা সময় কি হবে,0,crime
ভাই এইসব ভিডিও আর দিয়েন্না। কারণ এইসব দেখলে মনেহয় মাফিয়া হয়ে যাই আর নিজের হাতে এই জারজদের শাস্তি দেই।,0,crime
এই মহিলার কথা আমার কেন জানি বিশ্বাস হয় না,0,crime
ঠিক আছে বিচার 👌👌👌👌,0,crime
কাইদায়া কোন কাম নাই,0,crime
আপনার বলার ধরন টা দারুন 🤣🤣,0,crime
লুচ্চার বিচার না করে এখন কে ভিডিও ছারছে তাকে খুঁজবে । এই হল বাংলাদেশের আইন ।,0,crime
জারা এইকানে দারিয়ে দেখছিলো এরা পুরুষ নামে হিজরা এই ভাই আমি বলতেচাই এই দেশের জন্য মুক্তি যুদ্ধারা জীবন দিয়েছে যদি এই দেশের জন্য মুক্তি যুদ্ধারা জীবন দিতে পারে তাহলে আমরা কেনো এই ভাই রিফাত কে সন্তাসীর হাত তেকে বাঁচাতে জীবন দিবো না কেনো দাড়িয়ে তাকা লোক গুলা কি পুরুষ না ওরা।,0,crime
এই মেয়ে সম্পুর্ণ ভাবে জড়িত। কারণ দেখাই যাচ্ছে তারা আগে থেকেই মিটিং করে আসছে। এই মেয়ে জড়িত আছে।,0,crime
তার মুখের আচরণ দেখেও তো মনে হচ্ছে সে অপরাধ করেছে,0,crime
এত কাহিনী করার পরেও এত সুন্দর করে গান কিভাবে গাইতে পারেন আমার মাথায় ঢুকছেনা,0,crime
জনগন তোমাদের লুচ্চামি জানে কিন্তু তোমার সামনে পিছনে বসে থাকা বলদাগুলা বোঝে না কারন তারাও আকাম করে তোমার ছায়ায় আশ্রয় নিয়েছে।,0,crime
এতো কষ্ট দেওয়া হয়েছিলো নুসরাত কে,0,crime
মিন্নির বিচার চাই সে ত সমস্ত নাসতার মুল সেই হত্যা কাণ্ড ঘটিয়েছে এবং কুক্ষাত অপরাধীর মিন্নি এর মূল হোতা পরিকল্পিত ভাবে তিনি হত্যা করিয়েছে এমন মেয়ে যেনো পৃথিবীতে আর না হয় তাই মিন্নির বিচার চাই মিন্নি মেয়ে বলে পার পেয়ে যাবে সেটা হবেনা অপরাধী যেই হোক শাস্তি তাকে পেতে হবে মাননীয় প্রধান মন্ত্রী এ কথা প্রায়ই বলেন দেখি মিন্নির বিচার হয় কিনা,0,crime
হাইরে কপালঁ সব শেষ কিছুই থাকলোনা,0,crime
অবশ্যই মুন্নি কে পুলিশি হেফাজতে নিতে হবে তাহলে আসল রহস্য বের হয়ে আসবে মুন্নি এই হত্যার পিছনে দায়ী,0,crime
আমি চাই অধ্যাপকে শয়তাকে জন সমুখে ফাঁশি দেওয়া হোক কারণ এই ওর কারনে কত আজ কত বোন সামি ছাড়া৷ কত মা সন্তান ছাড়া কত ছেলে ৷ মেয়ে বাবা ছাড়া হবে তার পরে ও অপরাধ হিসেবে শাস্তি পেতেই হবে হে আল্লাহ আমদেরকে এই পাপী কাজ ৷ থেকে বাঁচার তৌফিক দাও আমিন,0,crime
আশে পাশে মানুষগুলো পশুর থেকেও খারাপ সবাই চেয়ে চেয়ে দেখলো ।,0,crime
এই ভিডিও তে বুঝা যায় তার স্ত্রী সম্পর্নু দায়ী এবং যরিত কি সুন্দর হাঁতে ধরে নিয়ে গেলো কিছুই বলেনি যখন কুপিয়ে রক্তাক্ত তখন ছেলেগুলো কে ধাক্কাধাক্কি করলেও,0,crime
মেয়েটা জড়িত পুরাই ক্লিয়ার,0,crime
জুতা দিয়ে পিটাইয়া শিক্ষা দেয়া উচিত।,0,crime
দাড়ি টুপি টকশ কথা গুলো অনেক বাল লাগলো।,0,crime
নুস্রাতের মাও এম্নে লাফিয়ে লাফিয়ে কেদেচে,0,crime
দেশের হোগা মারতাছে,0,crime
ভাই কি আর আমলে নিবে তা আমরা জানি মিনিটের খেলা দেখার পরেও আর কি তদন্ত করবে ডিসি কে প্রকাশে মারা হোক না হলে এরা ভালো হবেনা আর সরকারি দলের লোকজন তো আছে এটা শেষ হয়ে যাবে। আর পড়ে সবাই কে বলবে ওনাকে চাকরি থেকে বরখাস্ত করা হয়েছে কিছু টাকা জরিমানা আদায় করবে ।শালার দালাল দেশটাকে ধ্বংস করে দিচ্ছে।,0,crime
বালে,0,crime
পালতু যত্তসব,0,crime
ভিডিও ধারণকারীকে অসংখ্য ধন্যবাদ ভিডিও সহ যথার্থ প্রমাণ থাকার পরে ও দুই অপরাধীর বিচার হয়নি। প্রশংসনীয় বাংলাদেশের বিচার বিভাগ!,0,crime
এটা কোন ভিডিও হল অাগা গোড়া কিছুরই মিল নাই,0,crime
সরকারি বড় বড় কর্মকর্তাদের চরিএ এমনই হয়,0,crime
গলাটা তো ভালই!,0,crime
ডি সি পাসি চাই মেয়ে কে ওপাসি চাই,0,crime
ভিডিওটা এক মিনিটও না তবে কমান্ট গুলা পরতে পরতে পাঁচ মিনিট লাগলো সেই লাগলো পরতে এখানে মেনশোন জদি দেওয়া জাইতো তাহলে সব বন্ধুদের কমান্ট গুলা দেখাইতাম,0,crime
ইসলামের শরিয়তের মত বিচার করা হক। জিনা করা সাস্তি ইট পাথর মেরে ফেলা হক। তার কোন বেচে থাকা জায়েজ নয়। তাকে আল্লাহ কোন দিন মাফ করবেন্না।,0,crime
খুব খুব ভালো হয়েছে,0,crime
আমার একটু ও কস্ট লাগেনা শুধু যে মহিলার বাচ্চা হইছে তার জন্য কস্ট লাগে।কিন্তু যখন মনে পড়ে এই পাস্নড মহিলা পেটে বাচ্ছা নিয়া একটা মানুষককে খুন করছে?? তখন আর কস্ট লাগে না,0,crime
ভাই জাদের ধরা হইছে তাদেরকে টারমিনালের সামনে গুলি করে মেরে ফেলুন মানুষ দেখোক,0,crime
স্বামী নাই মনে হয়,0,crime
চিনিগুড়া আসামিদেরও ধরা হবে রিফাতের আসামির খুনিদের ধরা হবে সেইসাথে তিন্নি তাকে যদি পুলিশ হেফাজতে নজরদারিতে রেখে রিমান্ডে নিয়ে যায় তা হল আরো কিছু আলামত হয়তোবা আসতে পারে মানুষের সাথে জড়িত,0,crime
অই অপরাধীদের থানায় নেওয়া হউক😂😂,0,crime
ডাইরেক্ট ফাঁসি আফিল নাই প্রথমে শিক্ষা দিয়ে নাই বাচ্চা জন্ম দিয়ে শিক্ষা দেয় নাই এখন কান্না করছে সেই সময়টাই যখন ছোটকালে চশমাটা কোথায় ছিল বাবা মা,0,crime
পাপে বাপরে ছাড়ে না পাপ করছত সাজো ত ভুগতেই হবাে দােয়া করি অতি তাড়াতাড়ি যেন ফাঁসির রায় কার্য্য কর হয়? ধন্যবাদ ফােনী জেলার প্রাসাশনকে?,0,crime
হেতের শরীরের ভিতরে মাল আটকে আছে যার ফলে খালি মোছর মারতেছে 😉😉😉,0,crime
এখন ও কোল খালি হয় নাই । যদি হয় তখন বুঝবা নুসরাতের মায়ের কষ্ট,0,crime
নুসরাত এর জন্য দুয়া করবেন সবাই,0,crime
চরিএ খারাপ হলে যা হয় এখন শাক দিয়ে মাছ ঢাকার চেস্টা!,0,crime
নিন্দা জানাই,0,crime
ওই। এত। কিচু দরকার কি তাকে পাসি দিয়া দে খালস,0,crime
দেশে আর কোনো দিন উন্নত হবে না আমরা প্রবাসীরা নিজের দেশে ফিরে আশা হবে না,0,crime
হা হা হা লোল,0,crime
এভাবে আগুন দিয়ে তরতাজা মানুষকে পুড়িয়ে হত্যাকাণ্ডের আসামি দের ফাসির রায় কার্যকর করা হোক,0,crime
এটার প্রধান সমস্যা হচ্ছে আমাদের প্রধানমন্ত্রী নারী তাই নারীদের এত নির্যাতন হচ্ছে তার কোন বিচার কার্যক্রম চলতেছে না বাংলাদেশের সব সস্তা যদি বা আইন প্রয়োগ করতে পারত তাহলে কোন কর্মকর্তা এই কান্ড ঘটাতে পারত না।,0,crime
অনেক সুন্দর।,0,crime
রিফাতকে যারা কুপিয়ে হত্যা করেছে আল্লাহ্ তাদের বিচার করুন। আল্লাহ আমি তোমার কাছে বিচার চাই ।,0,crime
এখানে থাকবে চেয়ার টেবিল বিছানা আর বালিস কেন।।,0,crime
কেমন লাগে ছেলেমেয়েকে সঠিক শিক্ষা কি দিয়েছিলেন?,0,crime
স্যারের কোন দোষ নাই তোমার কোন দোষ নাই দোষ হচ্ছে সিসি ক্যামেরার। কারণ হচ্ছে ভিডিওটা তো করছেই সিসি ক্যামেরা। হা হা হা হা।,0,crime
সাধনা ঔষধালয় ডিসির সেবায় নিয়োজিত,0,crime
ওর বউ সব কিছু জানতো ভিডিও টা ভালো করে দেখুন ওর বউ কিনতু আছতে আছতে সামনে জাচছিলো তার পরে সে ওকে আটকাচছে এই মেয়ে টা ওনেক খারাপ সে চেয়েছিলো এক ঢিলে দুই পাখি শিখার হয় জেনো কইদিন জাক আবার দেখবেন কনো একটা ছেলেকে বিয়ে করবে জখন ভালো লাগবে না পরকিয়া করবে তার পরেই তো মারামারি শুরু হয় আমার ওনেক খারাপ লাগে মিনিটের মজার জননো একটা জিবন কেনো নেই বরিশালের ওই দিকের মেয়ে রা ওনেকেই খারাপ হয় এরকম আমরা ওনেকেই জানি,0,crime
অভাক হওয়ার কী আছে এটা বাংলাদেশ ভাই,0,crime
ভিডিওটি দেখে বুঝলাম এখানে মিন্নি জরিতো আছে,0,crime
পাসি চায় জন্য সভার,0,crime
আকাম করেছে তাও তার কোন ক্ষতি করে নাই। ।।।তাকে ডিসির সাথে বিয়ে দিয়ে বাঁচার রাস্তা করে দেয়া হোক,0,crime
বাংলাদেশে এসব কী হচ্ছে সৌদি আরবের মতো আইন জদি সরকার করতো তাহলে বিনা কারনে মানুষকে মরতে হতো না,0,crime
আমি থেকে বলছি আমার মতে মিন্নি অপরাধী কারন তার আগের সামি যেহেতু বেঁচে আছে । আর তার আগের সামি নয়ন পন্ডই যেহেতু রিফাত কে মেরেছে এরকম নারীর জায়গা বাংলাদেশে হওয়া উচিত নয় । আর বাংলাদেশের মাটি ও এরকম নারীর নছিব হওয়া উচিত নয়,0,crime
এটা লুইচ্চা ডিসি এ সব সরল মনে করেছে। সুতরাং এটা কোন অপরাধ না।।,0,crime
যদি মিন্নির বিচার না য়ন তাহলে বুঝবো রিফাতের বিচার হয় নাই।,0,crime
এতে কষ্ট পাওয়ার কিছু নাই যার গায়ে আগুন দেওয়া হয়েছিল ঐ মেয়ে টা কত যন্ত্রণা ভোগ করতে হয়েছিল কিন্তু এতটাই পুড়ে ছিল বাঁচাতে পারেনি ?,0,crime
একদম হোক কথা বস,0,crime
যার ধর্মীয় জ্ঞান নেই সে যত বড় বিদ্যান হোক না কেন সে সু শিক্ষিত নয়। অশিক্ষিত লোক দ্বারা যেকোন ধরনের অপরাধ হতে পারে।,0,crime
মিন্নির ফাসি চাই ভিডিও টা ভালোভাবে দেখলে বুঝা যায় মিন্নি চেয়েছিল রিফাতকে মার ধোর করুক কিন্তু জানে মেরে পেলবে সেটা হয়ত ভাবে নাই তাই ছুরি দিয়ে মারার আগে চুপচাপ ছিল ?,0,crime
তাকে এতো কোপালো মেয়েকে কেনো কোপালো না,0,crime
আমি একটি ব্যাপার বুঝলাম না এত নিখুঁত ক্লিয়ার ভিডিও এখন কি ভাবে বের হলো । যখন রিফাত কে হত্যা করে সেই ভিডিওতে এত মানুষ দেখা যায়নি । এই ভিডিওতে এত মানুষ কোথায় থেকে এলো কেউ বলবেন এটা একটা বানোয়াট ভিডিও । মিন্নি যদি তাঁর স্বামীকে হত্যা প্লান করেই থাকে তাকে জনস্মুখে কেনো মারবে ।মিন্নি কি কচি বাচ্চা যে তাঁর স্বামীকে হত্যা করে জেলে ঘানি টানবে তাও প্রকাশ্যে দিবালোকে । এটা সম্পূর্ণ বানোয়াট ভিডিও?,0,crime
এমন ভাবে মিন্নি রিফাত কে ধরে রিকসা করে জায় নি আপনারা কেনো জে এসব ভিডিও করেন না বুঝি না কিছু,0,crime
ভাল লেগেছে,0,crime
স্রষ্টা মানুষকে সম্মানিত করেন আবার ক্ষনিকেই কিভাবে ধুলিসাৎ করে দেখুন। ডিসি সাহেব সারা জীবনের অর্জন আজ মিনিটেই কাবু করলেন। আল্লাহ আমাদের সম্মান দিয়ে আবার কেড়ে নিয়েন না আপনি মহান সর্বশক্তিমান।,0,crime
নারী হলো মেয়ের জাদ মনি তুমি কী ইকটুও বাবনি আজ আমি জেই কাজটা করছি কাল আমার কী হবে হয়তো তখন তোমার বিবেকের চোখটা ঢাকা ছিলো যদি খোলা রাখতা তাহলে আজ তোমার এই পরিনতি হতো না তোমার জন্য মায়া হয়না মায়া হয় অবুঝ শিশুর জন্য সেতো কো অপরাধ করেনি সবার কাছে অনুরোধ এই শিশুটার দিকে থাকিয়ে তারে ফাঁসির থিকে মাপ করা জাইনা,0,crime
কাইন্দা লাভ নাই,0,crime
শিশু দর্শন কারিদের দরুন তৈরি করুন দেখি।কে যানে এখানে কোন স্বার্থ আছে নাকি টাকা ওলা লোক বটে।,0,crime
একরকম একটা মাদক ব্যাবসায়ী খুনি র সাথে কে ঘর করতে চাই যারা এরকম ইভটিজিং সীকার শুধু তারাই বোঝে।কাউকে বলতে পারেনা দোষ হয় মাঝখান দিয়ে মেয়েদের।,0,crime
ধনের জলে ভাসিয়ে দিলাম গুদের ঠিকানা চুদার ভয়ে করলে তুমি অন্য বাহানা তবু তুমার জন্য ধন আমার খারা যে রাখব আমি শুধু তুমাকে চুদব । ধনকে নিয়ে চুদলে মেলা করলে ধনের অবহেলা তবু ও ধন খাড়া হয় ধনালে রাত্রি বেলা যদি কারো মাসিক নামে পাটা বুদু আমার নামে আমার ধন খাড়া যে রাখলাম। চুদতে থেক চুদাতে থেক আমি যে চাইব তবু তুমার জন্য ধন আমার খারা যে রাখব।দেবনা চুদন তুমায় চুদতে যদি না দাও আমায় এ ভাবে দড়ব আমি চিরদিন দুধ যে তুমার যদি কারো মাসিক নামে আজ ও স্বপ্ন দোষে আমি আজ শরীর কেলালাম চুদতে থেক চুদাতে থেক আমি যে চাইব তবু তুমার জন্য ধন আমার খারা যে রাখব।,0,crime
আমার চাই মিনি জে বিচার হক মিনি এই কাজে পারছেন সুয়র জরতো,0,crime
ভিডিও ফুটেজ দেখলাম আনেক কয়েক জন রিফাতকে ধরে নিয়ে যায় শুধু দুই জনকে কেনো সাজা দেয়া হলো,0,crime
মেয়েটা কি অভিনয় করল সেটা বড় কথা নয় অপরাধীর সাজা হোক সেটা বড় কথা,0,crime
জমির জায়গায় জমি থাকবে চাষ করে খান। এর কোন দোষ নেই দোষ হল কার,0,crime
? পর থেকে ? মাঝ খানে ? মিনিট সেকেন্ড সময় টুকো এ নেই । প্রথম আলো কে বলছি এই অংশটুকু আপনাদের আমরা দেখতে চাই। মনে হচ্ছে এখানেই কোন ঘটনা লুকিয়ে আছে যা আপনারা লুকাতে চাচ্ছেন।,0,crime
বমি আর মাথা ব্যাথা হওয়ার কথা। কিন্তু অজ্ঞান হয়ে পড়ে গেল কেন 😋,0,crime
কিচ্ছাটা ভাল লাগলে অবশ্যই কমেন্ট করে জানাবেন।লাইক বাটনে ক্লিক করে লাইক দেবেন।শেয়ার এবং সাবস্কাইব করে আমাদের সাথেই থাকুন।যাতে নতুন নতুন ভিডিও উপভোগ করতে আমাদের সাথেই থাকুন,0,crime
ভাইয়া সবাই ভালো করে দেখেন মেয়েটা প্রথমে রিফাত কে বাঁচি নি যখন কুপাতে থাকে তখন সেই ভালো সাজার জন্য তাকে বাচঁতে থাকে দেখেন মেয়েটা কত খারাপ,0,crime
পেক না তাকে রিমান্ড এ নিয়ে গেলে সটিক তত্ত্ব চলে আসবে,0,crime
সাগর রুনি খুন হেয়েছে তাদের কোন বিচার হয়েছে,0,crime
যারা দাঁড়িয়ে দাঁড়িয়ে দেখল তাদেরকে এক বছর করে সাজা দেওয়া দরকার যারা একেবারে কাছ থেকে দেখেছে তাদেরকে যেন একটু বেশি দেওয়া হয়,0,crime
বাংলাদেশে জনসম্মুখে বিচার কার্য সম্পন্ন করা উচিত তাহলে অপরাধীরা কিছুটা ভয় পাবে।,0,crime
এই দেশের সরকার আইন কি তাই জানে না। আবার বিচার করবে কি করে?? আজ এই সরকার যদি ইসলামিক কায়দায় বিচার করত তাহলে এত তাজা প্রাণ ঝরে যেত না।। এমন এক সমাজে বাস করে আমরা।।,0,crime
আগে একবার বিয়ে হওয়া প্রেম করা এগুলো কি খুনের চেয়েও বড় অপরাধ !? যদি তাই না হয় তাহলে যারা প্রকাশ্যে কুপিয়ে হত্যা করল তাদেরকে ছেড়ে যারা রিফাতের স্ত্রির চারিত্রিক সনদ নিয়ে গবেষনায় লিপ্ত আছেন তারা কি পানি গোলা করে খুনীদেরকে বাঁচানোর পথ তৈরি করে দিচ্ছেন না তো ?? ভেবে দেখবেন !? ⬇ যারা কুপিয়ে হত্যা করল আগে তাদেরকে জনসম্মুখে শিরচ্ছেদ করা হোক তারপর অন্য কেউ জড়িত থাকলে তার বিচার করা হোক,0,crime
আল্লাহ পাক আজ একটা ঠিক বিচার দিলেন কি দোষ ছিল নুসরাতের,0,crime
এ খুনিদের মিন্নি সহ জন কে ফাঁসি দেওয়া হোক,0,crime
আসসালামুয়ালাইকুম। আসলে তো ডিসি কে ভালো মানুষের মতো মনে হচ্ছে। এই ডিসিকে নষ্ট করেছে এই সুন্দরী মেয়ে। দুঃখজনক হলেও সত্য মমকে আগুনের কাছে নেয়া হলে তা গলে যাবে। তাই আমাদের নারীসমাজকে পর্দায় আনতে হবে। তানাহলে হাজারো ডিসি এরকম মেয়ের চক্করে পড়ে নিজের ও দেশের মান সম্মান হারাবে। এব্যাপারে দেশের সরকারকে আমরা জানাবো আপনি কুরআনের আইন চালু করুন। তাতে দেশ ও দেশের মানুষ রক্ষা পাবে।,0,crime
কলেজের কেমেরা শুধু এক দিকে কেনো? গেটের সামনে কি কেমেরা নাই?,0,crime
ভাইয়া পুরোটা রাইট বললেন আর আমি চাই এই ফালতু মহিলারে আগে কঠিন শাস্তি হোক একটা মেয়ে হয়ে কিভাবে আরেকটা মেয়ের সংসার ভাংতে পারে 😥 ইচ্ছে করছে থাপ্পড় মাড়ি মহিলাটারে,0,crime
ছি ছি ছি😆😆,0,crime
কি ভাবে সাজানো নিজের বিবেকের কাছে প্রশ্ন করেন তো,0,crime
এই ভিডিওটা সামাজিক যোগাযোগমাধ্যমে বেশি করে প্রচার করা দরকার।আসল অপরাধী যে ঐ মেয়েটা সবাই এটা জানুক।,0,crime
এখানে ব্ল্যাকমেল অথবা মানসিক সমস্যার কোন প্রশ্নই আসেনা উনি অপরাধী এবং উনার শাস্তি হওয়াটাই উনার পাওনা,0,crime
মিন্নি জড়িত আছে ওর ফাঁসি চাই ওর মা জড়িত আছে,0,crime
এক হাতে তালি বাজে না আর আমার ধারণা অনুযায়ী মেয়েটা সবচেয়ে বড় অপরাধী বিভিন্ন তথ্য অনুযায়ী জানতে পারলাম মেয়েটির আরো দুইটা বিয়ে হয়েছিল অবশেষে আমরা দুজনের পর্যাপ্ত পরিমাণ শাস্তি চাই,0,crime
এরি মাঝে তো দেখি পুজাও করে? কারা এই পুজা করে?,0,crime
মেয়েরা কি করে চাকরী করবে কারও কাছে মেয়েরা নিরাপদ না।।।,0,crime
মিন্নিই তো ঘটোনার মুল,0,crime
মা বোন আপনারা কান্না করতেছেন দেখে খুব কষ্ট পেলাম কিন্তু এটার বিচার হতে হবে কারন এমন দেখে অন্যরা শিক্ষা নিবে আপনারা কান্না করতেছেন কাদের জন্য মারে জানি এক জন মা কত কষ্ট করে সন্তান লালনপালন করে এমন কি শিক্ষা দিয়েছেন তাদের আজ এই পরিনতি আজ মুসলিম হয়ে মানুষ পুড়িয়ে মারে তারা তো মানুষ হতে পারে না মারে তুমি এখন কান্না করতেছো তোমার বুকটা খালি হবে ঠিক ঐ মেয়েটির মার বুকটা খালি করেছে আল্লাহ তুমি আমাদের মাপ করে দাও আমিন,0,crime
এ জন্যই ছেলেদের চাকরি হয় না শুধু মেয়েদেরই হয় এগুলো করার জন্য তাই সকল ভাইদের প্রতি আমার আকুল আবেদন যে কারো বোন বা বউকে একা বা কোন ফাদের চাকরি নিতে দিবেন না।,0,crime
ওজেঅনপুসকে কাপুর খুলেদেয় নিজের সামি ছারাএর বিচার করে বুজ,0,crime
সব দোষী গেরেফতার হয়েছে এক জন বাকি সেই হলো ওসি,0,crime
খুব ভাল,0,crime
ওদের ফাসি চাই,0,crime
খুনিদের বিচার চাই। মিন্নির ফাঁশি চাই,0,crime
এর পর এই খানে মেয়ের দােস জখন ডিসটার্ব করতাে তখন কেন তার মা বাবর কাছে বলে নাই আর কলেজে পড়া দরকার কি ছিলাে,0,crime
কথায় আছে ছূ,0,crime
পরিবেশটা সুন্দর ছিল স্যার,0,crime
রিফাত হত্যার মূল আসামি মিন্নি তা এই ভিডিও ফুটেজ এ প্রমানিত মিন্নিকে গ্রেফতার করতে সব তথ্য বেরিয়ে আসবে বলে মনে করি।,0,crime
হাতে বাচ্চা নিয়ে হাজির হয়েছিল জামিনের জন্য বেচারি ? 😂🤣😂🤣🤣😂😂🤣,0,crime
আসামী পক্ষের উকিলদের ও শাস্তি দরকার,0,crime
আল্লাহ পাক আমাদের সবাইকে মাফ করন আল্লাহ পাক আমাদের সবাইকে মাফ করন যখন এরা নুসরাত কে পুরিয়ে মেরে ছে না জানি মেয়ে টা কতো কস্ট পেয়েছে এরা তো তার এক অংশ পাইনি রে ভাই তুমি এদের নিয়ে ভিডিও টা করলে বাট একবার নুসরাত ভিডিও টা দেখো বুঝতে পারবে মেয়ে টা মারা জাবার আগে কিভাবে কেঁদে কেদে এক ফোটা পানি চেয়ে ছিলো এদের এমন হওয়া উচিত,0,crime
এখন কতো ধরনের কথা বলবে। যেমন ঃ তাকে ভয়ভীতি দেখিয়ে জোরপূর্বক ভাবে বাধ্য করে এমন করানো হয়েছে,0,crime
বিচার হবে বলে আমার মনে হয় না।,0,crime
কত বড় নির্লজ্জ হলে আবার ক্যামেরার সামনে দাঁড়িয়ে বাহাদুরি বক্তব্য দিচ্ছে।,0,crime
বউতো মেয়ের বয়সী,0,crime
মিনিট ওটা দেখেন নাই,0,crime
সারোয়ার আলম সার কে ধন্যবাদ,0,crime
মজাই মজা,0,crime
ভিডিও দেখে বুঝলাম মিন্নী অবশ্যই জরিত। স্বামীকে কুপিয়ে আহত করার পর কেউ কি এভাবে জুতা পায়ে দেয় আর ব্যাগ হাতে ঝুলিয়ে ট্যাঙ ট্যাঙ করে হেঁটে যেতে পারে?? স্ত্রী পাগল হয়ে যাবে। বুঝতে পারছি না প্রশাসন কেন মেয়ে টাকে জিজ্ঞাসা করছে না।,0,crime
মিন্নি আসল খুনি।ওর শাস্তি চাই,0,crime
এত দিনে বুঝতে পারলাম এই দেশে অপরাধী গান এত জনপ্রিয় হওয়ার কারণ কি! এই মেয়ের জন্য দুইটা মরছে অথচ মাইয়া নির্দোষ হিসাবে ঘটনা শেষে বেঁচে যাবে,0,crime
তিব্র নিন্দা জানাই ঐ ছাত্র নামধারী সন্ত্রাসীদের এবং ঘঠনায় জড়িত সকলের ফাঁসি দাবী করছি!!!।।।,0,crime
ডিজিটাল বাংলাদেশ।,0,crime
? তার স্বামীকে মারতে মারতে নিয়ে যাচ্ছে অথচ তার সেদিকে কোনো চিন্তাই নাই। আজিব লাগলো বিষয়টা।,0,crime
আল্লাহ সকলকে দ্বীনের বুঝ দান করুন,0,crime
দুজনেই অপরাধী তবে মেয়েটা কে বেশি আগ্রহী মনে হয়েছে মনে হচ্ছে মেয়েটা যেন ইচ্ছা করেই চাইছিল এটা ভাইরাল হোক,0,crime
এইসব দেখেও লোকদের শিক্ষা হয়না আল্লাহ সবাই কে হেদায়েত দান করুন,0,crime
ভিডিও টা অনেকবার দেখলাম মনে হয় মিন্নী জড়িত।,0,crime
যেই দেশের সরকার অবৈধ সেই দেশে এই সব তো সাধারন ঘটনা। সরকারের সব অফিস আদালতে এই সব হওয়া টা স্বাভাবিক কারন ডিজিটাল সরকারের ডিজিটাল উন্নয়নেরই এটা ডিজিটাল যৌন কর্ম।,0,crime
খুবই খুসি হলাম,0,crime
এজন্যই বলে একজনের পাপের ঘানি সংসারের সবার টানতে হয়।। এনারা এখন ও মনে করেন এনাদের সোনার ছেলেরা একদম নির্দোষ,0,crime
মিন্নির ভিডিও কাবিননামা সব আছে। এগুলা মিথ্যা নয় কখনোই। মিন্নির কথা মুখস্ত।লক্ষ্য করলে বুঝবেন।,0,crime
মিন্নি হচ্ছে দুসি ওর সক্তবির হওয়া উচিত,0,crime
এই রকম বিচার সবসময়ই হইত আর কোন দিন মায়ের বোক খালি হতনা,0,crime
এদের ফাঁসি হওয়াই উচিত যদি তারা সত্যি অপরাধি হয়প থাকে নুসরাত তোদের কী কতি করেছিলো,0,crime
মিন্নি কে আগে গ্রেফতার করা উচিৎ। এর বিচার চাই,0,crime
এদের দুজনকে জনগনের সামনে হত্যা করা হোক।,0,crime
সত্যি যদি অপরাধ করে থাকে হাজারোও কান্না কাটি করে লাব নাই আল্লাহ পাক বিচার করবেয়ে,0,crime
যখন কলেজের ভিতরে মারছিল তখনই তো ঐ মেয়েটা তার বাপ অথবা শশুরকে ফোন করার কথা! সে মাদক ব্যবসার সাথে জড়িত কি না সে বিষয়েও তদন্ত হওয়া দরকার।,0,crime
আব্রারের খুনিদের এভাবে ফাশির রায় দেওয়া হউক,0,crime
দৌড়ে পালিয়ে আর কি হবে রে পাগলী,0,crime
ভাই আপনাকে অনেক ধন্যবাদ সঠিক টা তুলে ধরার জন্য সরকারের কাছে আমার আবেদন রইল মিননির ফাঁসি দেওয়া হোক,0,crime
বড্ড মায়া হচ্ছে বেচারার জন্য এত সুন্দর কণ্ঠ! ধরা না খেলে এখানে সবাই সাধু। ধরা খেলে ধর শালা।,0,crime
এটাতে বুঝা যায় তার বউ যে মেইন কালপিট নিয়ে যাওয়ার সময় ধরলো না আর কোপানোর সময় ধরলো😡😡পুরাটাই একটা প্লেন ছিলো বুঝা যাচ্ছে😔😔,0,crime
একটা জিনিস অবাক করা বিষয় যে রিফাত হত্যার আসামিদের কেউ পাঞ্জাবী পরা ছিল না। কিন্তু এই শর্টফিল্মে মূল অপরাধীকেই পাঞ্জাবী পরানো হয়েছে। ধর্মীয় পোশাকের সাথে মিল থাকে এমন পোশাক কেন অপরাধীকে পরিয়ে অভিনয় করানো হয়। ধর্মীয় প্রতিকগুলো নিয়ে এতো চুলকানি কেন????????????????,0,crime
মহিলাটাকে সেফুদা চাচার কাছে পাঠিয়ে দাও,0,crime
মিনিট,0,crime
আসসালামু আলাইকুম আমাদের বাংলাদেশের পুলিশ বাহিনী এবং লাইভ বাহিনী যারা আমাদের কোটি মানুষের দায়িত্ব নিয়েছেন তাদেরকে উদ্দেশ্য করে একটা কথা বলতেছি নয়ন কে ক্রসফায়ার করা হোক এবং রিয়াদের স্ত্রী যদি আগে ওর সাথে কোন সম্পর্ক থেকে থাকে এবং বিবাহ বন্ধনে বেঁধে থাকে ওকে ফাঁসি দেওয়া হোক দেখবেন দেশ সোনার বাংলাদেশ একদম ঠান্ডা হয়ে যাবে আর কোনো মেয়ের সাহস পাবে না ছেলেদের মনে এরকম ধরনের,0,crime
তাঁরা তারি ফাঁসি হোক,0,crime
সরকারী টাকা খেয়ে মাথা গরম হয়ে গেছে। ওর মাথায় বরফ দেয়া দরকার।,0,crime
দেশের যে অবস্থা কিছু করার নাই।এই বিচার টা হাদিস মোতাবেক হওয়া উচিত বলে আমি মনে করি।,0,crime
দুই অপরাধীর বিচার জনসম্মূকে করা উচিত।,0,crime
সব দোষ জনগনের ইসলাম অনুযায়ী বিচার হওয়ার দরকার মাটির নিচে শরিল পুতে ঢুরামেরে মেরে ফেলা উচিত,0,crime
তারা যদি দোশি হয়ে থাকে তাদের সাজা হওয়া দরকার। আল্লাহ সব কিছু দেখেন আমাদের মনে রাখা দরকার আমিন।,0,crime
এতো সুন্দর বউ রেখে কেন একটা নষ্টা মেয়ের সাথে পুষ্টিনাষ্টি করতে গেলী এরকম একটা বউ আল্লাহর পক্ষ হতে নেয়ামত বুজলিনারে বুজলিনা।,0,crime
আমার খুব ভালো লাগতাছে,0,crime
ডিসি আইনের লোক খয়ে কু করম করে পরিবেশ টা খুব সুন্দর না কোন হৈই চই আছে তারপর কাল কে বলিবে ডিসি এটা গুজব,0,crime
ভাই আপনাকে আওয়ামী লীগ কত টাকা দিয়েছে । আপনার ফ্যামিলি ও তো মনে হচ্ছে এমন,0,crime
আমরা সবাই কে ফাঁসি চাই,0,crime
এমন কান্না দেখে খোব কস্ট হয় একটা মানুষ যদি অপরাধ করার আগে একটু ভাবতো তাহলে হয়তো আজ এতো গুলো মানুষকে আজ কান্নাহ করতে হতনা আপন জন হারানো কষ্ট ভুগ করতে হতনা দোয়া করি আল্লাহতালার কছে এমন অপরাধ থেকে মানব জাতীকে বীরত রাখে ? আম িন,0,crime
নয়নকে মারা হলো কেন গ্রেফতার না করে ? মিন্নির সাথে একটি কুচক্রি জড়িত বলে মনে করছ। তাছাড়া নয়ন িএকাই পুলিশের সাথে যুদ্ধ করলো । এটা কি মেনে নেওয়া যায়? নাকি নয়ন বেচেঁ থাকলে রাঘব বোয়ালদের নাম বেরিয়ে আসতো তাই তাকে পৃথিবী থেকে স্বাক্ষির খাতা থেকে মুছে ফেলা হলো ।অন্যান্নদের কেন নরমালি গ্রেফতার করা হলো । সবাই তো একই অপরাধের অপরাদী তাহলে কেন এমন ঘটনা ঘটলো । খুব সুক্ষভাবে তদন্ত করা উচিত বলে মনে করছি। যাতে সত্যটা বেরিয়ে আসে । অপরাধীর শাস্তি হোক এটাই কামনা ।,0,crime
মালিয়শিয়া সবধরনের খেলার লাইসেন্স চলে মালায়শিয়া সরকারের বড় অংকের আয়,0,crime
ওর মত মেয়েরা দেশে হাজার হাজার জারস সন্তান জন্মে দিছে তারা এখন ইসলাম নিয়ে বাজে কতা বলে,0,crime
সত্য কি লিখতো।নুসরাত মরে গেছে তাই বলে সবাই ভুলে গেছে নুসরাত পানি পানি করে মারা গেছে।তোদের জালেম সন্তানরা খুন করেছে নুসরাত কে,0,crime
কিছুই বুঝতে পারলাম না,0,crime
বরগুনার মেয়েরা অনেক মিথ্যা কথা বলো বেশি,0,crime
এমন মেয়ের জন্য এমন ভদ্র ছেলে কিছুইনা গাজাখোর হিরোন্সিই ওদের দরকার যাদের কোনো ফিলিংস নেই।। ভদ্র ছেলে হলেএমন মেয়ের জন্য দরকার আমার মত মোটামুটি সাস্থ্যবান শক্তিশালী ছেলে,0,crime
এখানে প্রশাশন জরিত আছে। আগে তাদের শটিক বিচার করুন। কিলাবের আসে পাসে থাকা আইনের করমো রত মানুশ দের আগে ছাছতি দেন।,0,crime
সত্য কখনো থাকেনা চাপা মিথ্যা কথা বলে এগুলো দেওয়া যাবে ধামাচাপা এটা যে সত্যি কারের ভিডিও ফুটেজ তাহা ভালো করেই যাচ্ছে বুঝা,0,crime
এই লোকের পরিবারের এখন কী অবস্থা জানতে ইচ্ছে করছে। এর যা বয়স ছেলেমেয়ে তো বুঝবার মত বড় হয়েছে ।,0,crime
ঐ মহিলাকে রিমানডে নেওয়া হোক,0,crime
মানুষ পাপ করবে পাপের শাস্তি মানুষকেই পেতে হবে। দুনিয়ায় গুপনে পাপ করে মাফ পাওয়া জায় কিন্তু আখিরাতে আল্লাহ তায়ালা তার বিচার করবেন।টিক তেমনি দুনিয়াতে প্রকাশে সবার সামনে একজনকে পুরিয়ে মরা হলে তার মাফ দুনিয়াতে হওয়া দরকার।,0,crime
মিন্নি ও খুনি,0,crime
সরকারের যত অফিস আছে সবই অনৈতিক কর্মকাণ্ড হয়ে আসছে ।শুধু তাই নয় সব ধরনের অপরাধ বেড়েছে বহুগুণ তার পিছনে সরকার ব্যাপক সমস্যা পড়বে যদি প্রশাসনের কাছে এমন কিছু জাতি লজ্জিত ।তার সঠিক তদন্ত করে আইনের আওতায় আনা হউক ।,0,crime
এই মহিলার স্বামীর এখন কেমন প্রতিক্রিয়া সেটা একটু জানাবেন,0,crime
আমাদের বোন নুরছাত কি কম কষ্টের মাঝে দুয়ার মায়া ছারচে😥😥,0,crime
একজন স্বামীকে ধরে নিয়ে যাচ্ছে গুন্ডারা আর পিছনে পিছনে বউ হেঁটে যাচ্ছে কি স্বাভাবিকভাবে,0,crime
বিকৃত রুচীর মানুষ গুলোর চেহারাগুলো ও বিকৃত হয়।,0,crime
খুনিরা কি খিনের বিচার করে,0,crime
এই গুলি আমার জানা মতে বছর আগে থেকে চলছে।,0,crime
মামুর বেটা ফাইসস্যা গেলো,0,crime
চি,0,crime
আগে মিন্নিকে ধরাহক তাইলে সব সত্যটা বার হবে,0,crime
বছর লাগবে মূল ঘটনা উদঘাটন করতে। আর বিচার সে তো অনন্ত কালের বিষ।,0,crime
একটা মানুষ মারা গেলে তার জন্য মানুষ মানববন্ধন করা হয় কিন্তু এতো মানুষের সামনে একটা মানুষকে তিন চার জনে কুপিয়ে হত্যা করলো কিন্তু কেউ এগিয়ে গেল না শুধু চেয়ে চেয়ে দেখল তারা কি মানুষ না জানোয়ার আর এখন সোলো গান করে তারা যে খুনিদের ফাঁসি চাই খুনিদের আগে যারা দাড়িয়ে দেখছে তাদের বিচার করা দরকার ছিল আগে,0,crime
নুসরাতকে মারার আগে মনে ছিলোনা এখন তো কাদতেই হবে,0,crime
আমি আরো হাসতে চাই😊😊😊,0,crime
ওরা খুনি ওদের ফাঁসি হবেনা তোর ফাঁসি হবে তোর ফাঁসি হলে ভাল হত তোদের জন্য অপরাধীরা বেচে যায়,0,crime
এইসব ভিডিও তোদেরকে কে বানাইতে বলছে এরা বিশ্বের বাচ্চারা,0,crime
কি সুন্দর বাংলাদেশ এমন দেশকে জুতা মারতে মন চায় যেখানে কোন বিচার নাই,0,crime
আর কত কি দেখবো! এরাই আমাদের সোনার ছেলে বাহ্,0,crime
সঠিক কথা তুলে ধরার জন্য ধন্যবাদ,0,crime
মাগী,0,crime
দোষীদের সাথে কিছু নির্দোষও ফেসে যাচ্ছে বলে মনে হচ্ছে।,0,crime
যত তারা তারি পারেন এ পাপিদের কে ফাসি দিয়ে দিন এ দের পরিবারের কাননা দেখলে চলবে না নুরাতের পরিবার এর চেয়ে বেশি কাননা করেছে তাই আর দেরি তারা তারি দিয়ে দিন,0,crime
মাইয়াটা বুঝে ডিসির কিছু হবে না । দুষ কার এইটা তুমার বলতে হবে না। কিন্তু তুমার চাকরি মনে হয় না আর থাকবে,0,crime
মদ ও জুয়া সম্পর্কে আল্লাহ পাক কি বলেছেন বলেছেন ? তারা তোমাকে মদ ও জুয়া সম্পর্কে জিজ্ঞেস করে। বলে দাও এতদুভয়ের মধ্যে রয়েছে মহাপাপ। আর মানুষের জন্যে উপকারিতাও রয়েছে তবে এগুলোর পাপ উপকারিতা অপেক্ষা অনেক বড়। আর তোমার কাছে জিজ্ঞেস করে কি তারা ব্যয় করবে? বলে দাও নিজেদের প্রয়োজনীয় ব্যয়ের পর যা বাঁচে তাই খরচ করবে। এভাবেই আল্লাহ তোমাদের জন্যে নির্দেশ সুস্পষ্টরূপে বর্ণনা করেন যাতে তোমরা চিন্তা করতে পার। সুরা বাকারা আয়াত হে মুমিনগণ এই যে মদ জুয়া প্রতিমা এবং ভাগ্য নির্ধারক শরসমূহ এসব শয়তানের অপবিত্র কার্য বৈ তো নয়। অতএব এগুলো থেকে বেঁচে থাক যাতে তোমরা কল্যাণপ্রাপ্ত হও। সুরা মায়েদা আয়াত শয়তান তো চায় মদ ও জুয়ার মাধ্যমে তোমাদের পরস্পরের মাঝে শুত্রুতা ও বিদ্বেষ সঞ্চারিত করে দিতে এবং আল্লাহর স্মরণ ও নামায থেকে তোমাদেরকে বিরত রাখতে। অতএব তোমরা এখন ও কি নিবৃত্ত হবে? সুরা মায়েদা আয়াত আমর কুরআন পড়িনা বুঝিনা ও মানিনা । আমাদের উর বিপদ আসবেনা কেন ?,0,crime
বড় খুনি তো মিনিন,0,crime
এক দিনে কোনো কিছু হয় না লেনদেন গরমিলের কারণেই হয়তো এটা ফাঁস করা হয়েছে,0,crime
মিন্ন ফোন কল চেক করা হক তাহলো সব সত্য বের হয়ে জাবে সত্যি বাংলাদেশ এখন আর সাধীন দেশ রং বাজি দিয়ে ভরে গেছে করা থেকে করা বেবসতাছা নেয়া হক,0,crime
তোমার তুলে দরা পুটেজ এবং সাজিয়ে কথা গুলো বুজিয়ে বলার জন্য অনেক ধন্যবাদ,0,crime
আমার মনে হচ্ছে তার বউ এর সাথে জড়িত,0,crime
কংকে,0,crime
নুসরাত রে যখন হত্যা করেছিল তাই এমনইভাবে নুসরাতের মা বাবা নুসরাত কেঁদেছিল,0,crime
মিন্নি কে এক নাম্বার আশামি করা হক,0,crime
রিফাত ফরাজির ফাসি চাই।,0,crime
লিংক লাগলে জানাও,0,crime
এখনো আত্বগ্লানি নেয়,0,crime
চলে যাইতেছে তার পিছনে পিছনে ভিডিও করা দরকার কি অপরাধী কে না অপরাধীর অপরাধ কে ঘৃণা করতে শিখুন।,0,crime
ভাইয়েরা সত্যতা জাচাই না কোরে কাউকে দোশি বলা ঠিক হবেনা ভাই,0,crime
মায়েদের কান্না দেখে আমার অনেক কষ্ট হচ্ছে কিন্তু নূসরাতের মা এই ভাবে কান্না করছে তখন তার মেয়ের জন্য কেমন করেছে কিন্তু ওদের ফাঁসি চাই ফাঁসি চাই ফাঁসি চাই যাতে আর কোন নূসরাত এই ভাবে হত্যা না হয়,0,crime
সত্যিকারের ভিলেন যিনি ভিডিওতে নায়িকা তিনি 👉মিন্নী,0,crime
ফাঁসি হবে কবে,0,crime
ওদের লাশ দেখতে চাি,0,crime
কলেজের সামনে প্রকাশ্য দিবালোকে শত মানুষ এর উপ্সথিতিতে একটি ছেলেকে কুপিয়ে যাচ্ছে কতিপয় যুবক ফেরাতে চেষ্টা করছে একটি মেয়ে হা করে তামাশা দেখছে সবাই ! কি ভয়াবহ চিত্র! ওহে গরুগন! হাম্বা রবে প্রতিবাদ কর!,0,crime
হিজাব পরে বেশির ভাগই খারাপ মেয়ে।।।,0,crime
রিফাতের রক্তাত্ত বুক নিয়ে যেভাবে চলে গেলো তাতে মিন্নির দিকে মুখ তুলে তাকাতেও ওর ঘৃন্না লাগছে এমন একটা অনুভতি দেখা গেলো মিন্নিকে যতই নির্দশি প্রমান করুক না কেনো এই মিন্নি সারাজিবন রিফাতের কাছে অপরাধি হয়ে থাকবে আর কোনো আইনের সময় নষ্টের দরকার নেই রিফাতের চলে যাওয়ার দৃশ্যই ক্লিয়ার করে দেই মিন্নির ওই মনে কত পেচ ছিল,0,crime
এগুলা আমাদের বিসিএস ক্যাডার😝😜,0,crime
ছি মিন্নি!আমাদের পরিচিত বা কাছের কারো গায়ে কেউ হাত তুললে আমরা সেটা সহ্য করতে পারি না।।আর সেখানে তো রিফাত তুমার স্বামী ছিল।। কিভাবে পারলে মডেল এর মত কিরে হেটে যেতে!!তুমার উচিৎ ছিল প্রথমেই ওদের থামানু।।বাধা দেউয়া তোমার দোষ আছে কিনা জানি না তুমার এই কাজ টা আমার ভাল লাগলো না😞😞,0,crime
হাই,0,crime
যত তারা ফাঁসি দিবে কান্না ও থেমে যাবে তাড়াতাড়ি,0,crime
এই ভিডিওতে প্রমাণিত হল মিন্নী আসলেই দোষী,0,crime
মেয়েটির হাত রয়েছে এ জায়গায় অভিনয় করেছেন এখন,0,crime
মিন্নির শাস্তি চাই,0,crime
মিন্নি খুনের সাথে জড়িত সন্দেহে রিফাত ফরাজীকে রিমান্ডে বেপক জিজ্ঞাসাবাদ করা হোক |মিন্নি তার স্বামীকে ধরিয়ে দিতে বা সহযুগিতা করতেছে ভিডিওতে এমনটি বুঝাযাচ্ছে প্রয়োজনে মিন্নিকে পুলিশি হেফাজতে জিজ্ঞাসাবাদ করা হোক সাধারণ জনগণের দাবি রেজাল্ট পাওয়া যাবে |,0,crime
আসুন আমরা সবাই সমআলচনা থেকে দুরে থাকি ইনশাআল্লাহ,0,crime
যখন নয়নের সঙ্গে টলাটলি করছিল তখন মনে ছিল না মন্নীর রিফাতকে বিয়ে করতে গেল কেন,0,crime
কি বলতে চান তার কোন দোষ নাই অবশ্যই ডিসির সাজা হোক আমাদের সবার দাবি,0,crime
মিন্নিকে যদি শাস্তি দেওয়া না হয় তাহলে আমরা মানব বন্ধন করতে বাধ্য হবো আর অবশ্যই পুলিশের উপর থেকে আমাদের ভরসা উঠে যাবে,0,crime
মান সম্মান আললাহর হাতে সকল প্রশংসা আল্লাহর জন্য এখন কি উপাই কতগুলো মানুষ এখন বেকার হলো তার সম্মান যেন আললাহ ফেরত দেন আমিন,0,crime
সবাই কে বলচি পুলিস কি সব সময় মারা মারির পরেই অাসে বেস্সা মিন্নিকে ও পাসিতে জুলানো হোক,0,crime
খারাপ করার সময় টের পাও না দিন চোরের এক দিন হাওদের,0,crime
কে করবে কার বিচার সব জায়গাতে চলের অনিয়ম একটাই একটাকে দিয়ে পার পাচ্ছে !,0,crime
আর মিন্নির প্রচুর সমস্যা আছে । তার দেয়া তথ্য প্রথম থেকেই ওলোট পালোট ওগুলা কই? ।। করলে ভালো কিছু কর। গরু ছাগলের কাম বাদ দে,0,crime
মেয়ে টাকে মারার সময় মনে ছিলো না।,0,crime
এই মহিলাকে ফাসি দেওয়া হোক,0,crime
খুব সুন্দর একটি কিচ্ছা ভালো লাগলো ধন্যবাদ দাদা। হিরো কাজিম,0,crime
দেশের বিতর রোহিংগারা রাজনীতি করে এই গোলা দেকেন না,0,crime
আমি আপনার সাথে একমত,0,crime
দূত বিচার কার্যকর করতে হবে সময় দেয়া উচিত নয়,0,crime
এগুলা সাংবাদিকের বাড়াবাড়ি! ঈদের পর তাদের দেখা হয়েছে তাই একটু কোলাকুলি করতেছে। আপনারাই বলেন পরিবেশটা শান্ত না কোন হৈচৈ আছে🤣🤣,0,crime
আমি এই রায়ে খুশি হয়েছি কিন্তু সংকায় আছি আপিলে আবার খালাস দেয়া না হয়।,0,crime
মিন্নি ফাসি।চাই😭😭😭😭😭😭,0,crime
রিফাত কে যখন থেকে জন ধরে নিয়ে যাচ্ছে তখন মিন্নি আস্তে আস্তে হাটছিলো আর বারবার কলেজের ভিতরে তাকাচ্ছিলো আর যখন সবাই ওরে হাত দিয়ে মারতেছিলো তখন মিন্নি আস্তে আস্তে হেটে যাচ্ছিলো যখন কোপাচ্ছিলো তখন দৌড়ে গিয়ে যে কোপাচ্ছে তাকে জরায়া ধরতেছে মানে নয়ন কে।কিন্তু একবারও কি রিফাত কে জরাইয়া ধরতে পারতোনা মিন্নি যদি রিফাত কে জরাইয়া ধরে রাখতো তাহলে ওর উপর দিয়ে গিয়ে কোপ দিতনা আসল কথা হলো এখানে মেইন আসামি মিন্নি আমার মতে ওরে যদি রিমান্ডে নেওয়া হতো সব বের হয়ে আসতো যে কিভাবে প্ল্যান করে মারছে মিন্নি কে আসলেই কোপ খাওয়ার পর যখন ওরা চলে আসলো তখন রিফাতও হয়তো বুজতে পেরেছে যে মিন্নি আমাকে কতটুকু ভালোবাসে তাই একবারও মিন্নির কাছে ফিরে আসেনি যদি মিন্নির ভালোবাসা সত্যি হতো তাহলে রিফাত বেচে যেতো আল্লাহ পাক হয়তো চায়নাই যে এরকম নারীর স্বামী থাকুক আল্লাহ তুমি মিন্নির বিচার কইরো এরকম মিন্নি যেনো আর য় না হয়। মিন্নির বিচার চাই,0,crime
সালের বিচার কইরা কুল পাই না এগুলির বিচার কখন করবে আমার সোনার বাংলা আমি তোমায় ???,0,crime
মিনিটের ভিডিওতে তুমি ভাইরাল !!!! তোমার সন্তানের বল কি হবে কাল !!!!,0,crime
মাল ঠিক অাছে,0,crime
এদিকে স্বামী কে সবাই টেনে হিঁচড়ে নিয়ে যাচ্ছে আর স্ত্রী নাচতে নাচতে যাচ্ছে। আর সবাই তাকিয়ে দেখছে সবাই যদি একত্রিত হয়ে সামনে এগিয়ে যেতো তাহলে হয়ত ছেলেটি আজ বেঁচে থাকত। হায়রে মানুষ,0,crime
কাহিনী না জাইন্না ফিল্ম করে,0,crime
মহিলা ডিসির কাছে জিম্মি অাছে তাই উল্টো পালটা বকতে অাছে।।,0,crime
এটা আমি লীগ করছে থেকে তদন্তের প্রয়োজন যদি কোন বিএনপি নেতা থাকতো তাহলে কোন তদন্তের প্রয়োজন ছিল না তাকে যাবজ্জীবন জীবন কারাদণ্ড,0,crime
কে বলে বাংলাদেশে আইন নেই। জনগনের সামনে ফাসি হওয়া উচিত ছিলো।,0,crime
শিশু টার জন্য কস্ট হচ্ছে।মা টাকে ফাঁসি না দেয়ে জাবতজীবন দিলে ভাল হত,0,crime
এটা রিমোভ করা উচিৎ,0,crime
মিন্নি সাথে জড়িত ফুটেজ দেখে যা বুঝা গেলো,0,crime
দুজনকেই আইনের আলতায় আনা দরকার,0,crime
যত জন এখানে জড়িত চিলো সবাই কে এক মাসের ভিতরে এই দুনিয়াই থেকে বিদায় দিতে হবে কোন ধরনের কারা দন্ড বা যাবত জীবন চাই না হয় ফাঁসি না হয় ক্রস ফায়ার,0,crime
মজা তুমিও পাইছ আমিও পাইছি ! জ্ঞান হারানোর কি আছে 😆,0,crime
যারা মিন্নির বিরূদ্দে একটি লাইক দিবেন,0,crime
বেশি করে মহিলাদের চাকুরি দাও,0,crime
বিয়ে দেওয়া হোক,0,crime
এসব কান্না হচ্ছে ভন্ড কান্না নুসরাতের গায়ে আগুন দেয়ার আগে ভাবেনি কেনো এই জানোয়ার গুলো মনে করছে দেশে বিচার নাই আরে জানোয়াররা এখনো দেশে বিচার আছে এবং থাকবে ফাঁসি কার্যকর তারতারি করার জন্য প্রধানমন্ত্রীর কাছে অনুরোধ করছি,0,crime
চিন্তাভাবনার লেভেল কি?,0,crime
আপুকে সবাই সহযোগিতা করুন,0,crime
ভাই মিনিটের ভিডিও পাই না তো। শুধু মিনিটের ভিডিও পাই। একমত হলে লাইক চাই।,0,crime
আমি বুজলাম মিন্নি প্রথমে বুজতে পারে নাই তার স্বামিকে ওরা মেরে ফেলবে হয়তো খুনিরা নিয়ে জাচেছ একটা রফাদফা করবে কিন্তু জখন দেখছে তার স্বামিকে খুনিরা মেরে পেলতেছে তখন মুন্নি তার স্বামিকে প্রানপন চেস্টা করেছিল বাচানোর জন্য। প্রথম থেকে মুন্নি আরেকটু সচেতনতা পরিচয় দেওয়া উচিৎ ছিল,0,crime
শতভাগ দোষ ঐ চরিত্র হীন ডিসির,0,crime
এখনো কি এর চাকরি আছে নাকি,0,crime
নয়নের আগে রিফাত ফরাজিকে ক্রসফায়ার করা উচিত ছিলো আর এই মিন্নি খারাপ শয়তান মেয়ে ফাঁসি দেওয়া হক এর জন্য আজ এই পরিনতি এই খারাপ মেয়ে কে ফাঁসি না দিলে জাতি ও মায়ের সাথে বেইমানি করা হবে সবার ফাঁসি চাই যারা জরিতো আছে সবার ফাঁসি চাই সাধিন দেশে সাধিন মতো বাঁচতে আই আমি জর্দান থেকে বলছি,0,crime
কোন দেশে বাস করি আমরা এই প্রমান থাকা সত্ত্বেও এই অসভ্য এবং বরবর লোকটার পদ বহাল থাকে কিভাবে দুখজনক হলেও এই দেশে জন্ম গ্রহন করে আমি লজ্জিত এবং জাতি বিপদগ্রস্ত।,0,crime
এই ভিডিও দেখার পর কমেন্ট না করে পারলাম না এর সাথে মিন্নি জড়িত তার প্রমান তার স্বাভাবিক হাটা স্বামীকে মারতে মারতে নিয়ে যাচ্ছে অথচ তার কোন প্রতিবাদ নেই এর নাম ভালোবাসা,0,crime
মিন্নি কে ফাসি দেয়া হোক সে অপরাধী,0,crime
আমার ধরনা মিন্ন এদের সাথে জরিতো আছে মিন্নি রিমান্ডে দাবি জানাই এবং এই মিন্নি র ফাঁসি চাই,0,crime
এই বাংলাদেশের মানুষ এত টা পাষান এই মিন্নি মেয়ে টা একটা সয়তান ফালতু মেয়ে টা একবার রিফাত কে জরিয়ে ধরে বললো না যে আমাকে কোটাও আমাকে মারো তুমরা মিন্নি তো রিফাতের কাছেই আসে নাই মিন্নি তো অর পুরনো প্রেমিকের সঙ্গে ছিলো,0,crime
কোন জেলার ঘটনা আগে সেইটা জানেন ভালো করে সব আসামী যে নুসরাতের হবে তা কোনো কথা না।। এই ঘটনা ফরিদ পুরের না যে সুনে টাইটেল তো ভালো ই দিওয়া শিখছেন,0,crime
মিন্নির ফাসি চাই অার কত ছেলেদের জীবন নষ করবা,0,crime
মিন্নিকেে রিমান্ডে নেওয়া হোক,0,crime
বিচার চাই,0,crime
তার ব উ কে পাশি ছাই,0,crime
বেশি করছে মনে হয় 😜,0,crime
দু জনেই চরম উত্তেজনায় মানুষিক বিপর্যস্ত হয়ে যৌন কর্মে লিপ্ত হওয়ায় তাহারা সিসিটিভি ক্যামেরা লক্ষ করেন নাই! দুষ্ট প্রকাশককে আইনের আওতায় এনে পুরস্কৃত করা হোক।,0,crime
ওকে ফাসি দেয়া হোক,0,crime
কোন জাতির উন্নতি অবনতি এবং ধ্বংস নির্ভর করে ওই জাতীর শিক্ষা ও সংস্কৃতির উন্নতি অবনতির ধ্বংসের উপরে এক্ষেত্ৰে ভাষার একটি মূখ্য ভূমিকা রয়েছে মুসলিম জাতির মূল ভাষা আরবী ভাষা এবং মূল শিক্ষা তাওহীদের সঠিক শিক্ষা যদিও জাতি গঠনে এবং আন্তর্জাতিক সম্পর্ক সুদৃঢ় করার ক্ষেত্রে অন্যান্য ভাষাগুলোর পারদর্শিতাও অত্যন্ত জরুরি আলহামদুলিল্লাহ পবিত্র কুরআনের প্রথম নির্দেশই শিক্ষা গ্রহণের নির্দেশ রাসুল সঃ হিব্রু ভাষায় পারদর্শিতা অর্জনের জন্য এক সাহাবীকে নির্দেশ দিয়েছিলেন এবং তিনি মাত্র দিনেই পারদর্শিতা অর্জন করেছিলেন আলহামদুলিল্লাহ্ ইসরাইলে তিনটি ভাষা শিক্ষা করা অত্যাবশ্যক,0,crime
মিন্নি এ খুনের সঙ্গে জড়িত তাকে ফাসি দাওয়া হক।,0,crime
আমাদের জামালপুরের জন্য এটা একটা কলঙ্ক আমরা এই জঘন্য ব্যাক্তির দৃস্টান্ত মুলক শাস্তি চাই ও পদত্যাগ চাই,0,crime
হিসেব বোঝ নাহ,0,crime
আবরাররের হত্যার মামলার আসামি দের এরকম বিচার চাই। তাহলে ভাবো বাংলাদেশের বিচার হয়।,0,crime
ভাই বেশিক্ষন রাখতে পারে না মিনিটের মত পারছে। হারবালে সমাধান,0,crime
এই সানজিদা কি বিবাহিতো,0,crime
মিন্নিকে ক্রসফায়ারে দেওয়া হক।সিসি টিভি এর ফুটেজে দেখে বুঝা যাচ্ছে মূল পরিকল্পনা কারী মিন্নি।,0,crime
সটিক কাহিনী করেছেন আর বেশী করে করবেন আশা রাখি,0,crime
প্রতিটি অফিসে এরকম সেক্রেটারী বসদের সাথে এসব কাজ করে থাকে কেউ ধরা পরে কেউ পরে না বেচারা ডিসি,0,crime
লাশ।দেখতে চাই টা লাশ।,0,crime
ডিসির রুমে যেই বেক্তি ক্যামেরা টা লাগাইছে থাকে গোয়েন্দা বিভাগে চাকরি দেওয়া হোক !!!,0,crime
স্পষ্ট দেখা যাচ্ছে যে মিননি অপরাধী কারণ ছেলেগুলো যখন তার স্বামীকে ধরে নিয়ে যাচ্ছে তখনই সে পিছে পিছে দৌড়ানো উচিত ছিল সেটা সে না করে স্বাভাবিক ভাবে হাটে আর লোক দেখানোর জন্য তখন সে বাঁচানোর চেষ্টা করো এটা কিন্তু ঠিক না আমার মতে মিননি অপরাধী ওর জন্যই তো আজ দুটো ছেলে শেষ আমার মতে ওকে ফাঁসি দেওয়া উচিত তাহলে ওর মতো ভিডিও আরো অনেক ঘরে জন্মে যেতে পারে,0,crime
এই মহিলা আকাম করে অপরাধ করেছে আবার হিজাবকে কলঙ্কিত করেছে এর এবং ডিসির দৃষ্টান্তমূলক শাস্তি দাবি করছি,0,crime
মাননীয় স্পিকার আমি চোদনা হয়ে গেলাম,0,crime
আরেকটু ডেলে দিলে সব ঠিক হয়ে যাবে,0,crime
রিফাত ফরাজী এর প্রকাশে ক্রসফায়ার করা হোক,0,crime
হায় রে জীবন সাধারন মানুষ হলে কি করতো,0,crime
একটি হত্যা করতে জন ফাসি কি জঘন্য,0,crime
দেশ,0,crime
যে ভিডিও করেছে থাকে চাকরী দেওয়ার দরকার সে একটী ভালো কাজ করেছে ! দেশটাতে নোংরামিই ভরে গেছে,0,crime
এদের কাছ থেকে আমরা কি আশা করতে পারি এক জন ডিসি জদি হয় এ রকম,0,crime
এটা যে জামালপুরের সেই ডিসির ভিডিও তার কি প্রমাণ। এখানেতো আর চেহারা দেখা যাচ্চেনা। অন্যকেউ তো হতে পারে।,0,crime
আমাকে বাচার মতো বাচতে দিন কথাটার মধ্যেও রহস্য আছে। ডিসি সাহেব জটিল গুটি চালবে মহিলাটার উপর,0,crime
এখন কান্না করো কেনো ভাই যখন মেয়েটা কে পুরিয়ে মারছো তখন মেয়ের কান্না দেখে তোমাদের কান্না আসে নাই এখন কান্না করো কেনো,0,crime
সাবস্ক্রাইব করে সাথে থাকুন দারুন সব খবর সবার আগে জানতে,0,crime
এখানে তযন্তের কি আছে ভিডিও দেখলে ছলে ওরা কারা ভিডিও ক্লিয়ার দেখা জায়,0,crime
ভাই আপনাকে ধন্যবাদ,0,crime
ভালই তো লাগলো,0,crime
জেই ভাবে ভাষণ দিলেন ডিসি এখন সম্মান কোথায় গেলো,0,crime
কিস্সার কথা গলো সবই মিথ্যা।এই কিচ্ছার সব কথা মিন্নির সাজানো কথা।মিন্নি নিজের ইচ্ছায় নয়ন কে বিয়ে করে।ও একটা কাল নাগিনী।ওর ফাসি চায়।,0,crime
খুব খুশি হয়েছি,0,crime
সবাই কি ছবির শ্যুটিং দেখতেছে????,0,crime
একটা মেয়ের জন্য বাংলাদেশের সব মেয়েরা খারাপ না তাই আমি মনে করি এই মেয়ের বিচার হওয়া উচিত,0,crime
খুনিদের বিচার করা দরকার নাই এদের কে গুলি করে হত্যা করা ভালো,0,crime
হালায় যে লুইচ্চা চোর হালার বডি লেংগুয়েজে বোঝা যাচ্ছে হালায় মিথ্যা কথাগুলা গুছিয়ে বলতে পারতেছে না🤭🤭🤭🤭,0,crime
এই ওএসডি শেষ সরকার সাহস করবে কিনা এর বেশি কিছু করতে ভোলার জেলা পরিষদের ঘটনা কি আপনাদের মনে আছে,0,crime
দোষ কি শুধুই ডিসির ফ্রি আলকাতরা আমরা সাদা লুঙ্গিতে নিতে দিধা করিনা সেইখানে একটি মেয়ে তার দিচ্ছে ভিডিও টিতে ডিসির চাইতে লোভি নারির আগ্রহী বিশি ছিলো।,0,crime
জয় বাংলা সুন্দর হইছে,0,crime
তর বুদাই আগুন লাগাই দিব,0,crime
রাইট রাইট রাইট,0,crime
এইটা এডিট না এইটা রিয়েল এদের দুজনের কঠিন শাস্তি হওয়া উচিত,0,crime
এই দুশ্চরিত্র ডিসি চাকরিচ্যুত করা হোক,0,crime
আপনি বলেছেন দুজনের সম্মতি ক্রমে এইগুলো হলে অপরাধ নয়। আপনার কাছে আমার প্রশ্ন তাহলে অপরাধ কোনটা,0,crime
ভিডিও কে ছাড়ছে তদন্ত হবে তার বিরুদ্ধে😂,0,crime
পালাল কেন,0,crime
এ বছরের সেরা একটি গল্প | স্বল্পদৈর্ঘ্য চলচ্চিত্র বৃদ্ধাশ্রম | | পুরো ভিডিওটি দেখে আপনার মূল্যবান মতামত আমাদেরকে জানাবেন প্লিজ। শেয়ার করুন।,0,crime
প্রকাশ্য দিবালোকে এই নির্মম হত্যাকান্ড যারা ঘটিয়েছে সকলকেই নয়ন বন্ডের পরিনতি হওয়া উচিত বলে আমি মনে করি। আর ঘৃনা প্রকাশ করছি সেইসব লোকদের প্রতি যারা মিন্নি কে দোষারোপ করে ঘটনা ভিন্ন খাতে নেওয়ার চেষ্টায় লিপ্ত ।। আর সম্মানিত ভদ্রলোক মিন্নির হেটে যাওয়া আপনার চোখে পড়লো কিন্তু আপনার আমার মত যারা নয়ন বন্ডের দায়ের কোপের ভয়ে দৌড়ে পালাচ্ছিলো তারা এখানে কেউ আবার কমেন্ট করে মিন্নি কে গালমন্দ করছেন না তো।।।।।। আফসোস 😫☹☹☹😢😢,0,crime
সবই হলো জামায়াত শিবিরে পরিকল্পনা জয় বাংলা 🤣😅😂,0,crime
আমার চ্যালের ভাইরাল ভিডিওঃ,0,crime
মিন্নির ফাসি চাই সবাই,0,crime
বেয়াদবির ক্ষমা নেই,0,crime
দেখুন মাননীয় মন্ত্রী ওনি কিন্তুু তারিখে চুরি ডাকাতি হওয়া ভোটে আপনাদের হয়ে অবশ্যই অন্যান্য ডিসিদের মত সুকাজে কুকাজ সাহায্য করেছেন।সুতরাং শাস্তি যে সর্বোচ্চ পরিমাণ দিবেন সেটা জানা বুঝা শেষ।আসলে আপনারা সবগুলাই তার মত একেকটা মুখোশ পরা শয়তান।,0,crime
এই ভিডিও টি তে যুক্তি আছে 👌,0,crime
এদেশের মানুষদের নৈতিকতা বলতে বেশি কিছু নেই।। নৈতিক শিক্ষা দেওয়ার মত সামাজিক কোনো প্রতিষ্ঠানও নেই। যেগুলো রয়েছে সেগুলো এসব নোংরামি হালকাভাবে নেয়। এই জেলা প্রশাসকের পরিবারও নোংরা।,0,crime
এই খেলা এবার সামলাবে কে,0,crime
মিন্নী দাই আমরা চাই মিন্নীকে পুলিশের আওতায় আনা হক,0,crime
ফুটেজে সবকিছু এখানে সাক্ষী প্ৰমাণেৰ কোনো প্ৰয়োজন নাই। ফাচী । আজকে দিন পাৰ হয়ে যায় খুনিদেৰ ফাচী কেন হয়না? ঐ বাংলাদেশী গৰুৰ দল অতিশীঘ্ৰে ফাচীৰ ব্যাৱসথা কৰ ।,0,crime
শেখ হাসিনা নারী পুরুষের সমান অধিকার দিয়েছে ভাই।আওয়ামী লীগ মানেই বিনোদন।,0,crime
রিফাত এর কলার ধরে দুইজন ধরে নিয়ে যাচ্ছে।আর বউ পিছনে সাভাবিক ভাবে হেটে যাচ্ছে।ও তো বাসায় ফোন দিয়ে কাওকে আসতে বলতে পারতো।কিছু একটা কারন আছে,0,crime
বর্তমান ছেলেদের সমস্যা কি জানেন ? তারা সুন্দরী মেয়ে দেখলেই ভালো মনে করে অথচ একটি বারও চিন্তা করেনা তার চরিত্র আখলাক দ্বীনদারীর ব্যাপারে এই সব ভুলের জন্যই হয় জেলখানা হাসপাতাল বা কবরস্থানে চলে যায়,0,crime
হতবাক হচ্ছি সব সম্ভবের দেশ বাংলাদেশের কান্ড দেখে,0,crime
টাইম দিওনা অতি সত্তর ফাসিত লট কাঊ,0,crime
পোলা গুলা মিন্নির স্বামীকে ধরে নিয়ে যাচ্ছে আর ও আস্তে আস্তে হাটছে প্রথমে স্বামীকে বাঁচানোর কোনো চেষ্টা ছিলো না,0,crime
রিফাত কে জখন কোপাচ্ছে তখন মিন্নি। এদিক সেদিক ছুটা ছুটি করছে।কিন্তু এক বার ও িমন্নি ওর স্বামির কাছে জায়নি।মিন্নি জদি ওর স্বামি কে জরিয়ে দরতো তাহলে ওরা এতো কোপাতে পারতো না।আর মিন্নি কিভাবে মিডিয়ার কাছে সাবাবিক ভাবে সাক্খাত কার দিচ্ছে।ম্বামির জন্য একটু আফসুস করছেনা। সব মিলিয়ে আমাদের প্রবাসিদের একটা সদ্নেহ হচ্ছে তাই ব্যাপার টা ভালোবাবে তজন্ত করা দরকার।,0,crime
এদের কান্না দেখে কেন জানি খুব পৈশাচিক আনন্দ পাচ্ছি😊 নুসরাত একটা সময় এরকম কান্না করেছিল😭,0,crime
ছেলেরা অপরাদ করার সময় মনে ছিলো না,0,crime
এই হত্যাকাণ্ডে মেয়েটিও জড়িত আছে এতে কোন সন্দেহ নেই । তা না হলে খুনীর সাথে মেয়েটি হাসিমুখে কেক কেটেছিল কেন।😠😠 আর রিফাত কে কোপানোর সময় মেয়েটি এতবার অস্ত্রের সামনে গেল অথচ ওর শরীরে কোনো আঘাত লাগলো না।,0,crime
সহমত প্রকাশ,0,crime
মহিলাকে দেখে বোঝাই যায় দুই তিন বাচ্চার মা হবে আরেক জনের স্ত্রী এখন কথা হচ্ছে এটা গোপনে ভিডিও করেছে বলে আমরা দেখতে পাইছি এরকম হাজারো চাকরিজীবী মহিলা আছে যারা চাকরির ভয়ে কেউবা প্রমশনের লোভে এভাবে ফাও খাওয়াচ্ছে,0,crime
এরা কি জানেনা কার জন্য কান্না করছে নুছরাতকে কি ভয়ংকর ভাবে আগুনে পুরিয়ে মারছে লজ্জা হয়না এদের এই রকম মানুষ রুপি পশুর জন্য কান্না করতে যদি ওদের জায়গায় এরা হতো তো এরাকি চাইতো না খুনিদের ফাসি হোক হে তখন বলতো এদের ফাসি না হোক। বরং সব খুনিদের পাবলিকের সামনে আগুনে জ্যান্ত পুরিয়ে মারা হোক। জতটুক কস্ট নুছরাতকে দিছে তারাও অনুভব করুক। তবে মানোনিয় প্রধান মন্ত্রী জন নেত্রী জন দরদি শেখ হাসিনা সত্যি আপনাকে অসংখ্য ধন্যবাদ দোয়া করি আল্লা আপনাকে হেদায়েত করুক আমিন,0,crime
ডিসির আরেকটি অপকর্ম প্রকাশ পেল আরেকটি জীবন ধ্বংশ!!!,0,crime
চাকুরিতে নিয়োগের খেক্ষে অগ্রাধিকার দেয়াই হয় তাদের ভোগ করার জন্য।,0,crime
উচিত বিচার,0,crime
তা কি সত্য,0,crime
মিন্নির দোষটা কেন বলা হলোনা আপনি কি মিন্নির থেকে ঘুষ খাইছেন নাকি,0,crime
মেয়েটার শারিরিক ভাষাই বলে দিচ্ছে যে সে এই হত্যাকাণ্ডের সাথে জড়িত । মূল পরিকল্পনাকারী মিননি।।।,0,crime
চর চুরি করে আবার নিজেই বিচারক। হাইরে দেশের আইন।,0,crime
ভিডিও টা নকল হলেও সব কিছু নকল নয়,0,crime
মিনি আর লাস শিদানত কি,0,crime
পুলিশ কোথায় কেন এইমেয়েটা বিচার করছেনা এই মেয়েটাই দোষী,0,crime
যদি দাড়িওয়ালা হত তাহলে শয়তানা কামাল মুরগি কবির এরা টকশো শুরু করতো।,0,crime
এমন একটি রায় চয়েছিল বাংলার জনগণ। এইভাবে পতিটি বিচার হওয়া দরকার।,0,crime
এই সব দেখে মানুষ খারাপ হয়ে,0,crime
মিন্নি রিফাত ভাইরাল ছিলো প্রিয়া সাহা তার জায়গা নিলো প্রিয়া সাহা কে ভুলে গেলো কল্লা কাটার উদ্ভব হলো কল্লাকাটা থেমে গেলো ডেংগু মশা জন্ম নিলো ডেংগু মশার দিন শেষ চা ঢালার বাংলাদেশে রুমে ছিলো এসি! আড়ালে ছিলো সিসি আহারে বেচারা ডিসি! দেশবাসী দিচ্ছে ছিঃ ছিঃ,0,crime
সবাই করছে ছি ছি দোষ কি একার ডি সি,0,crime
সব দোষ সাধারণ মানুষের । এদের জন্য দেশে এত পরিমান রেপ হচ্ছে। এর পিছনে এদের মত রাঘবগোয়ালরা জরিত থাকায় দেশে কোন সুষ্ঠ বিচার হয়না। এধরনের যে কোন একজন ব্যক্তিকে যদি উপজুক্ত বিচারে আনা হতো তা দেখে আর কেহো এত বড় সাহস আর পেতনা।,0,crime
অয় মানুষদের কান্না শুনে যাদের দয়া হবে তারা ও অয় মানুষ খিব শিগরি ফাঁসি চাই ?,0,crime
অবিষপ্ত মিন্নি। ফজলুল হক হেলাল। উরুম ধুরুম মার খায় পতি ধীর পায়ে চলা মিন্নির গতি এবার তোরাই বল? বিষক্ত এই নারীর মনেই ছিলনা কি কোন ছল। সমুস্ত এই ঘটনার দায় ভাল করে দেখ মিন্নির গায় হায়রে কলঙ্কিনী। রুপ দেখিয়ে দুই পুরুষের করিলি জীবনহানি। তবু দেখে হায় মিন্নির পাছা। পেতে চায় তারে অনেক বাছা। লাইনে নাকি আধাবুড়া চাচা। সেও নাকি পেতে দিয়েছে কাছা হায়রে মনের রুচি। মিন্নিরে তোর রুপ যেন হায় কামুক প্রিয় লুচি।,0,crime
নয়নের থেকে বড়।। আসামি।মিন্নি।।নয়নের মিত্তু তে হবে না।।সরকারের কাছে মিন্নির ফাসি চাই,0,crime
রঘুনাথ দাদা কে অনেক ধন্যবাদ এত সুন্দর কিচ্ছা উপহার দেওয়ার জন্য ।,0,crime
নয়ন ও রিফাত এর বিচার করার মত কিছু নাই !!!!???আদালতের উচিৎ দেখা মাত্রই গুলি করা নির্দেশ দেয়া । কারণ তারা মাদক ছিনতাইয়ের খুন সহ আরো অনেক বড় বড় অপরাধ সাথে জড়িত । ওদের কারণে অনেক যুবক অপরাধ সাথে জড়িত হচ্ছে এবং মাদক সেবনও আসক্ত হচ্ছে । আদালতের কাছে অনুরোধ থাকবে ঐ দুইজনকে দেখা মাত্রই যেন দেয়া হয় এবং বাকিদের বিচারের মাধ্যমে সাজা প্রদান করা হোক। পোকামাকড়কে বিচার সাজা এই সব দেয়াও কি আছে ? দেখা মাত্রই মেরে না ফেললে আমাদের বাড়ি নোংরা হবে,0,crime
এটা তো নতুন কিছু নয় সারাজীবন বাংলাদেশের হয়ে থাকে এটা,0,crime
তারা সারাক্ষণ টাকার পিছনে দৌড়াদৌড়ি করে আর লুচ্চামি কাম করা আল্লাহর রাস্তায় কি তারা চিনবে নামাজ নাই কল মা নাই সারাদিন মেয়ে নিয়ে ব্যস্ত থাকে এটা বাস্তব বাংলাদেশ,0,crime
এগুলোর ফাঁসি চাই,0,crime
তরা তো মাত্র থেকে জন কান্না করছোত আর নুসরাতের সময় কুটি মানুষ কান্না করছি,0,crime
পাইছে বাংগালি জিনিস একটা! বছর পার হয়ে যাবে এই স্ক্যান্ডাল নিয়ে আর মিডিয়া ও আছে কাম কাজ নাই সস্তায় টি আর পি এইবার বাড়বেই! ডিসি তার সহকারির সাথে চুমা চাটি করে ইমরান হাশমি বনে গেছেন 🤣 আর দেশে চিপায় চিপায় জনি সিন্স মিয়া খলিফা রা ঘুরে বেড়াচ্ছে ওইটা নিয়ে কারো মাথা ব্যাথা নাই যত্তসব!!!,0,crime
তার সএী পিচে পিচে হেডে চলছে,0,crime
ওয়াও অনেক সুন্দর ভিডিও সম্পুর্ন কাহীনি খুব সুন্দর ফুটে উঠেছে ধন্যবাদ,0,crime
এখানে ঘটনা আপোষে ঘটেছে । এর থেকে আরো জঘন্য অপরাধ এদেশে সংগঠিত হচ্ছে।। ডিসি সাহেব তৃষ্ণার্থ মরুভূমিতে সেচ দিয়েছেন।এতে মেয়েটার উপকার হয়েছে।,0,crime
তারে জুতার মালা গলায় দিয়ে পুরা জামালপুর ঘুরানো উচিৎ,0,crime
আমিও প্রথম মিন্নির পক্ষে কথা বলছি এখন এই ভিডিওতে দেখদ যায় মিন্নি নিজে জড়িত তাকেও সাস্তি দেওয়া হক তাকেও রিমান্ডে দেওয়া হক এই ডাইনি টা কতো নিষ্টুর আমি প্রথম মিন্নির পক্ষ নিয়ে কথা বলছি লাম এখন এই ভিডিও টা দেখে আমি পুরো অভাক,0,crime
নারীদেরকে চাকরি দেওয়ার জন্য পাগল হয়ে যায় কেন তারা।।।,0,crime
টারে পাথর মেরে হত্যা করা উচিৎ,0,crime
আর কত অভিনয় করবে। এদের কে লেনটা করে পিটানোর প্রয়োজন ছিল,0,crime
এই মিন্নি মেয়েটাও খুনের সাথে জড়িত বলে আমি মনে করি।সি সি টিভি ক্যামেরার রেকর্ডে বুঝা যায়।ওকে আইনের আওতায় আনা হোক।,0,crime
ছি চি চি চি বাংলাদেশ নাম দরলে ল্যয লাগে,0,crime
আল্লাহ সবাইকে হেদায়েত দান করুন।আর এখন তো সবাই হুযুকে বাজ্ঞালি তাই লাফায় বেশি।সব জেনে পরে কথা বলেন সবাই।খারাপ রা ই এখন রাজত্ব করে বেশি।অনেক সময় আমরা ভুলের মাঝে থাকি।আল্লাহ যেন সঠিক বিচার করে।,0,crime
আল্লাহ গজব আসতে খুব দেরি নাই। ইসলামের সঠিক জ্ঞ্যান না থাকার কারনে লোভের বসবর্তী হয়ে মানুষের ইমান আকিদা নস্ট হয়ে গেছে।,0,crime
মিন্নি রিফাত কে মারার সাথে জরিতো আছে,0,crime
ওসি মোয়াজ্জিম যদি রেকডিং না করলে আমরা নুসরাতের সঠিক জবানবন্দি টা জানতে পারতাম না,0,crime
সারের দোষ নাই তোমার দোষ,0,crime
অবৈধ হাসিনা যতদিন ক্ষমতায় থাকবে ততদিন এমন চরিত্রহীনরাই একের পর এক এজাতীয় কর্মকাণ্ড চালিয়ে যাবে!,0,crime
এতো সুন্দর বউ থাকলে দুনিয়ার কোনো মেয়ের দিকে তাকাতে ইচ্ছে করবেনা।,0,crime
এই অমানবিক হত্যার জন্য রিফাত ফরাজীকেও কোপায়ে মারা হোক প্রয়োজনে কোপানোর দায়িত্ব জনগনের হাতে দেয়া হোক,0,crime
আজকাল সাংবাদিকরা কঠিন মজা নিতেছে,0,crime
সার তো মজা দিছে তাই সারের কনো দোস নাই।,0,crime
আরো কত ভাবে জুয়া খেলা খেলছে আর কত ক্লাব আছে এই দেশে আর ঐটা তো আর জাতি জানেনা।,0,crime
হা হা মজা পাইলাম,0,crime
আমরা এমন একটা দেশে বাস করি যে দেশে কোন বিচার নাই নিজেকে অনেক বেশি অপরাধি,0,crime
মারার পরে রিফাদ একদিকে মিন্নি উল্টা দিকে,0,crime
পরিবেশটা সুন্দর না ডিসি কি কেহ কে গালি দিয়েছে ডিসি সরাসরি ঢেলে দিয়েছে🤣🤣,0,crime
এর পর ও মেয়ে বিয়ে দেয়ার জন্য মেয়ের বাবা সরকারি অফিসার খুজে খুজে মেয়ে বিয়ে দেবে।,0,crime
পাপ সে যতোই করুক এর মানে কি বুঝিনি ? ওরা কাঁদছে নিজের মৃত্যু নিশ্চিত দেখে তবে ওরা একদমি কাদেনি নুসরাত নামের আরেকটি মানুষকে নির্মম ভাবে পুরিয়ে মেরে ফেলতে ওরা নিজের জীবনের জন্য বিচারের ফরিয়াদ জানাচ্ছে সেই আল্লার কাছেই যেই আল্লার সৃষ্টি নুসরাতও একজন আল্লার বান্দি ছিল । আল্লাহ্‌র কথা তখন স্বরন করেনি যখন তারা আল্লাহ্‌র সৃষ্টি একটা বান্দিকে মেরে ফেলার সিদ্ধান্ত নিয়েছিল এমন কি নির্মমভাবে পুরিয়ে মারার আগ মুহুর্ত পর্জন্তও তারা আল্লাহ্‌র কথা ভেবে হোলেও সিদ্ধান্ত থেকে ফিরে আসেনি । তাহলে সেই অমানুষদের জন্য তোমার এতো খাড়াপ লাগে কিসের জন্য ওদের কান্না দেখেই কি ? ইসলাম বলে যে মানুষ একটা বর্বর অপরাধির পক্ষে ব্যথিত হয় সে তাৎক্ষণিক সমান ভাবে একই অপরাধের অপরাধি হয়ে যায় । দুনিয়াতে তার বিচার হোক বা না হোক আল্লাহ্‌র আদালতে তার বিচার অবধারিত হয়ে রয় । প্রত্যেকটি খুনি ও খুনের ঘটনায় সহায়াতা কারিদের যেন এভাবেই সাজায় পরতে হয় সেটাই একমাত্র কাম্য হয়া উচিত মনে করি ।,0,crime
ডিসির রুমে কেমেরা আমিলাগেএচি,0,crime
এদের ফাঁসি দেওয়া হক।,0,crime
কথা শুনে মনে হচ্ছে উক্ত ঘটনার সাথে উনিই জড়িত!,0,crime
একে ফাঁস দেয়া হক,0,crime
সে দিনের মুক্তিযোদ্ধা দেশের জন্য মরন যোদ্ধ করেছে আজকে সে টাকার নেশার বাচার চেষ্টা করছে ৷,0,crime
যত সব ফালতু আগে সত্য ঘটনাটি দেখুন।,0,crime
ওরা শয়তান বাদী,0,crime
স্যারের দোষ কী ভাবে হবে সুযোগ দিয়েছেন বলেই তো স্যার সুযোগ নিয়েছে ভালো তো এগুলো করবেন আর বলবেন স্যার র্নিধোষ আমি র্নিধোষ। দেশে বিচার শুধুমাত্র সংবিধানের পাতায় আছে বাস্তবে না বলেই এগুলো দিন দিন বাড়ছে।,0,crime
এটা ঠিকি আছে এমনি হইছে দরি মাছ না ছূই পানি,0,crime
এর বিচার কবে হবে,0,crime
মাসের তদন্ত কমিটি ঘঠন করা হোক 😂😂😂,0,crime
ভাই ভিডিও টা এতো বড় না করে আসল জিনিস টা দিলেই তো পারতেন আর আঁসল অপরাধীদের ফাঁসি চাই!🇧🇩🇧🇩🇧🇩,0,crime
শুধু নয়নকে মেরে চুপ থাকলে চলবে না। যারা রিফাত হত্যার সাথে জড়িত সব খানকির পুলাদের ফাঁসি দিতে হবে। তবেই এমন অপরাধ করার সাহস কেউ দেখাবে না।,0,crime
সঠিক ভাবে দাঁড়ি টুপি ব্যবহার কারীর সম্মান আল্লাহ রক্ষা করেন,0,crime
এই হত্যাকান্ডে মিন্নীর হাত রয়েছে ভিডিও টাই প্রমান।,0,crime
কি কষ্ট হয়,0,crime
দেখলেও বাচ্চা এটোটা খারা হয় না।।।,0,crime
আল্লাহর বিচার কত অদ্ভুত যেখানে সুদ ঘোষ খাওয়ার অপরাধে গুন নাহ পরকাশ না করে যেনা বেভিচারের মত নিল জর্জ কাজের দ্বারা দুনিয়ার শাস্তি দিয়ে থাকেন। সম্মানে স্থানে অসম্মানজনক অবস্থা করে দিবেন। এই জন্য আমি বিনিত ভাবে অনুরোধ জানাই দেশের সকল মন্ত্রী সচিব ডিসি এস পি ওসি এবং সরকারি ও বেসরকারি সংস্থার ঊর্ধ্বতন কর্মকর্তাদের এ ঘটনায় থেকে শিক্ষা নিয়ে কাজ করার জন্য। আল্লাহ সবাইকে মাফ করেন।,0,crime
এখানে সম্পন্ন বুঝা যাচ্ছে ওর বৌ এটার সাথে জরিতো নয়তো কেনো মানুষের সামনে তার স্বামী কে নিয়ে গেলে কেউ এমন ভূমিকা থাকতে পারেনা,0,crime
এইগুলা সহ ফাঁসি দেওয়া উচিত।,0,crime
চোর ধোরলে চুরি করি নাই,0,crime
একটা সন্ত্রাসীর সাথে সম্পর্ক আছে জেনেও যে ছেলে চরিত্রহীন একটা মেয়েকে বিয়ে করে এবং যে অভিবাবকরা এই বিয়ে সম্পন্ন করে এরা সবাইই আসল খুনির সাথে সমানভাবে এই মৃত্যুর জন্য দায়ী। এটাই চরিত্রহীন সমাজের স্বাভাবিক পরিনতি।,0,crime
নাগিন,0,crime
কবির মজা পাইছ তাই না ছি ছি,0,crime
হাই কোয়ালিটির লুচ্চামির জন্য আঙ্কেলের একটা নোবেল পাওয়ার দরকার 😡 তা বলছি আঙ্কেল আপনার বাড়িতে বিষ নেই নিজের পোড়া মুখটা কাউকে না দেখিয়ে একটু খেয়ে শুয়ে পড়েন 😈,0,crime
তাদের বিচার নাম হলে সামাজিকতার মুল্যভোদের কলংক সরকার এড়িয়ে চলবেরে সরকার এড়িয়ে চলবেরে,0,crime
যে ভিডিও করছে তাকে অনেক ধন্যবাদ,0,crime
বেড়ায় গাছ খেয়ে ফেলে ছে ।,0,crime
এত মায়াবী স্ত্রী ঘরে থাকতে কী দরকার ছিল একটা অফিস সহায়িকার সাথে কুকর্ম করা।,0,crime
এই জন্য বলে সত সঙ্গে সরগো বাস আর অসত সঙ্গে সরবো নাস,0,crime
ঘুষ খাইলে কিছু হয় না। চাকুরি যায় না। অার এই বিষয়ে বরখাস্ত হলো,0,crime
আল্লাহ সবাইকে তুমি বুজদান করো আর কেউ যেন এমন অপরাধ না করে,0,crime
যদি চরিত্রহীন হয় ঠিক তখনই প্রশাসনও পঙ্গু হয়ে যায় নারী বাদী সমাজও এই কুকীর্তির সঙ্গে জড়িত নারী বাদী সমাজও র সঙ্গে পালিয়ে গেছে,0,crime
এত কিছু না করে ফাচি চাই,0,crime
এখানে আরও একটা বিষয় মিন্নি শুধু নয়নকে জড়িয়ে ধরে,0,crime
কেটে দেয়া হোক,0,crime
কেনো মেয়েটিকে হততা করার সময়।ভাবেনি।তখন ওই মেয়েটিও।আল্লা হকে।এবাবে ঢাকছে।আল্লাহর বিচার আল্লাহ দুনিয়াতেই।দেখিয়ে নেয়।,0,crime
ওদের লাথি মারা হউক,0,crime
সব চাইতে বেশি লজ্জা মহিলা দুই সরকারের এই যে একের পর এক ধষন চলছে আমি চাই যে ধষণ কারি তারে জেলে না নিয়ে সবার সামনে গুলি করা হক,0,crime
মিন্নিকেতো প্রথম বিডিওতেই দেখা যাচ্ছে ও কতোটা দুষি কারো শ্বামী এভাবে মারলে সে আবার ভেনেটি ব্যাগ কিভাবে তুলে নিয়ে যায় সধারন মারামারী ছারাতে গেলেই যে ছাড়া সে মার খায় আর এতো কোরুন দৃশ্য অকেতো ওরা কিছুই বল্লোনা কারন কি আপনাদের বিবেকে কি বলে আপনারাই বলেন,0,crime
আমি মনে করি শুধু নয়নই নয় এখানে যত জনতা আছে তারা প্রত্যেকে খুনি সাথে তার বউও,0,crime
আগেই এই মাগি টা কে ফাঁসি দেওয়া উচিত কারণ তাঁর করনে রিফাত এ মিতু হয়ে ছে রিফাত জখন তার হাত দরেছে তখন জলদি চলে যেতো তাহলেই রিফাত এ মিতু হইতে না,0,crime
ইনার চেহারা আর কথা বলার সময় ভীতবিহ্বল চেহারায় বলে দিচ্ছে উনি অপরাধী,0,crime
মূল অপরাধী মিন্নী,0,crime
রিফাত হত্যার বিচারটা ষদি এমনভাবে হত,0,crime
আরে ভাই তুই পালিয়ে গেলিনা কেন।আল্লাহ তোমায় বেহেস্ত দান করোক,0,crime
বরগুনার পুরুষ হিজটা ছেলে টাকে মারলো সবাই দেখলো কেউ এগিয়ে গেল না,0,crime
হেতে টুপি লাগাইছে।🤣,0,crime
জগত সংসার বড়ই কঠিন জীবনের চাহিদার কাছে আমরা সবাই অপরাধী। আজকের দিনে আমরা সবাই ভুলে গেছি সেই মহান উক্তিটি পাপকে ঘৃণা কর পাপীকে নয়,0,crime
নারীর সাধিনতা চায় ডিসির মতো শিয়াল গুলো রোমাঞ্চ করার জন্য এই রকম মহিলা দের অনেক ধরকার আর এই জন্য ছেলেদের কে চাকরি দেয় না এদের কে চাকরি দেয়,0,crime
আমি একটা কথা বলতে চাই দোষ কার তা জানিনা তবে এতো জনবহুল একটা রাসতায় কি করে একজনের ওপর এমন নিশংশ হামলা হতে পারে। রাসতায় কি কোন বিবেকবান মানুষই ছিলনা। মেয়েটার দোষ কতটুকু জানিনা তবে মেয়েটা একা তো এতগুলো ছেলের সাথে পারা সমভব না। আমরা শুধু সবার দোষ ধরতে পারি কিনতু কার বিপদে পাশে দাঁড়ায় না। কিনতু খুঁচিয়ে কথা বলার ওসতাদ আমরা বাংগালীজাতি।,0,crime
অামি শিওর মিন্নী ওদের সাথে জরিত,0,crime
সব টুকু ঘটনা না জেনে গানটি রচনা করা কি ঠিক হলো ??,0,crime
কাউকে এভাবে ফলো করা ঠিক নয়। খারাপ কাজ করলেও তার প্রাইভেসি নষ্ট করা ঠিক নয়।,0,crime
এরাই আবার নারী অধিকারের পক্ষে সোচ্চার 😂😂,0,crime
কিছু হবে না এ দেশে বিচার হবে বিচার বলে কিছু আছে দেশে,0,crime
কষ্ট লাগে এগুলি দেখলে,0,crime
কেমন যেন আনন্দ পা‌চ্ছি।ম‌নে হয় মান‌সিক বিকৃ‌তি হ‌য়ে‌ছে আমার।,0,crime
ডিসি সাহেব রোমিও যেখানে জুলীদের দেখেন তা একটু খেয়ে টেস্ট করে দেখেন 😍😎😂🤣,0,crime
মুক্তিযোদ্ধার বেতন বারাও বেশ করি,0,crime
খুনিদের বিচার চাই,0,crime
এই ভিডিও টা দেখলে বাংলাদেশের মানুষ সবাই বুঝতে পারবেন মিন্নি অপরাধী,0,crime
বিচার কার্য যেনো তাড়াতাড়ি শেষ হয় সেটাই কাম্য।,0,crime
সমস্যা নাই। উনি তো আর হুজুর না।,0,crime
রাসেদ খান কে ও রিমান্ড আবেদন করা হোক,0,crime
জেলা প্রশাসক কি প্রশাসন করে সে ক্যামেরার কথাও মনে নাই এমনি বায়ু চড়া মাথা নিজেকে সামলে চললে কি নিজের সম্মান বাড়ে না,0,crime
দেশের বিভিন্ন অফিসে এরকম ঘটনা ঘটে থাকে যা আমরা জানি না,0,crime
কথাই আছে চুরের দিন গিরস্থালি একদিন। আমাদের মাননিয় প্রদান মন্ত্রি শেখ হাসিনা এই বিষয় টি দেখবেন ওদেরকে আইনের আইতাই এনে শাস্তি দিবেন জেন আর এমন কারতে না পারে দেশের সসম্মানে রক্ষা করবেন ধন্যবাদ,0,crime
তার বউ সাথে অন্য কোন ছেলে সেক্স‌ করবে,0,crime
লজ্জা দুনিয়ায় থেকে উঠে গেছে আল্লাহ আমাদের সবাইকে হেদায়েত করুক।,0,crime
যত তাড়াতাড়ি ফাঁসি কার্যকর করা হোক,0,crime
ফাসি চাই খুনির,0,crime
ভুয়া নিউজ মিন্নী এখনো আটক হয়নি,0,crime
তুই মুখ দেখাস কি করে তোর আত্মহত্যা করা উচিৎ,0,crime
অপরাধ করার সময় সজনরা কোথায় ছিল,0,crime
সব জামাত শিবিরের চক্রান্ত এরা হ্যাকার লাগিয়েছে একটু পর কেউ একজন এটাই বলবে এদের জন্য ঠিকমতো রোমাঞ্চও করতে পারিনা বানীতে জনৈক নেতা,0,crime
সাংবাদিক ভাইয়েরা আপনারা প্রশন করেতছেন কিন্তু এখানে জারাই আটক হয়েছে তারাই বলছেন পুলিশ আসতেন মহিলাকে কেন প্রশন করছেন এই জায়গায় অবইদ আপনারা আগে জানেন না আপনারা কেমন সাংবাদিক,0,crime
মানুষ ও যা হইছে না জামালপুর এর ডিসি সাহেব না হয় একটু ঐ পজিশনে গেছেন😛😛😛😛তাতে জনগন যা পাইছে না😛😛মজা ডিসিও পাইছে😋😋মজা পার্টি ও পাইছে😜😜মজাতে মজা😛👰👳।।। এটা বাংলাদেশ 🇧🇩 ভাইজান।আর সে বাংলাদেশের একজন জেলা প্রসাশক আপনি আমি কোন বালটাও ফালাইতে পারবো না।।শুধু এমবি নষ্ট।।,0,crime
ডিচির সাথে ওরও বিচার হওয়া উচিত।,0,crime
কাট মুলল্লার ফাসি কোতাই,0,crime
এটা ফরিদপুরে ঘটনা ৷ এই সালা ইউটিঊবাররে সবাই জূতা মারেন ৷ ভুয়া নিঊজ দেয় ওই ৷,0,crime
এদের কোনো দোষ নাই ক্যামেরা যে লাগাইছে সব দোষ তার {♣য়া} মারা সারা,0,crime
সময় থাকতে বালো পথে চলো,0,crime
পুলিশের এসআই এর ফাঁসি দেওয়া হোক,0,crime
অন্য মানুষ কে কি বললো সেইটা কথা না আপনারা কি সিসি ক্যামেরা যে ভিডিও ধরা খায়ছে মিন্নি কত ঠান্ডা মাথায় হাটতাছে নয়নের সাথে তার বিয়েটা সে একবার বলে সাদা কাগজে সাইন নিছি আবার বলে বইয়ের মত একটা কিছুতে সাইন নিছে আবার বলে নয়নের সাথে যে পার্টিতে সে গেছে তাকে জোর করে নিছে আপনারা কি অন্ধ বোকা যে পার্টিতে ও কি ভাবে আচারন করছে তা দেখে যে কোন মানুষ বুজবে এটা জোর করে নিছে কিনা আর ওর কথা সুনে পুরা বুজা যাচ্ছে সে পুরা নাটক করতাছে পুলিশ না কথা বলার ধারন দেখে ধরতে পারে সে অপরাধী কিনা তাহলে এই মেয়ের বেলায় কেনো বুজতাছেনা পুলিশ ওর স্বামীকে কুপানোর আগে যতক্ষন মারছে এই মেয়ে তখন নরমাল ভাবে হাটছে কোন মেয়ে যদি দেখে তার স্বামীকে কেউ জোর করে টেনে হেঁচড়ে নিয়া যাচ্ছে মারতে মারতে ঐ মেয়ে তখন ঠান্ডায় মাথায় তখন কি করে হাটে আমি একজন মেয়ে হিসাবে বলছি এটা আমার জানা নাই আপনারা চোখ খুলে দেখুন সুনুন বুজুন আর এমন সঠিক বিচার করুন যেনো আর কোন মার কোল অকালে খালি না হয় বিনিত অনুরোধ পুলিশ পোশাশন আর মাননীয় প্রধানমন্ত্রীর কাছে সঠিক বিচার করুন।।।।। একটা সঠিক বিচার এমন করুন জেনো আর জীবনের ভয় থাকলে কেউ ধর্ষন খুন এ গুলা করবেনা।।।।।।।,0,crime
মিন্নি খুনের মুল এটা প্রমানিত। মিন্নির ফাসি চাই।,0,crime
আমি আর কি বলবো বাকি সবার মতো আমারো একটাই চাওয়া হয়তো যাবত জীবন না হয় ফাঁসি দুটোর একটা মঞ্জুর করা হোক।কারণ এই পাপিষ্ঠ গুলো বেচেঁ থাকলে মানব সম্প্রদায়ের অকল্যাণ হবে খুব শীগ্রই তাদের কে আইনের আওতায় আনা হোক প্রধানমন্ত্রীর কাছে আমাদের সকলের একটাই চাওয়া প্লিজ🙏 দেশের অনেক সম্মান হানি হয়েছে আর নয় ।,0,crime
কোনো সাজা হবে না এটা বাংলাদেশ,0,crime
ঘটনা এই রকম ছিল না,0,crime
কিছুই হবেনা। ও মাথা উঁচু করেই পদে বহাল থাকবে।,0,crime
মিন্নি কে রিমান্ডে নেওয়া হক সব বের হয়ে আসবে,0,crime
ভাইরাল হইছে জনমের ভাবে😁😁,0,crime
আল্লাহ আকবার,0,crime
এককতাফাসিচাই,0,crime
রাতারাতি ডিসি থেকে পর্নস্টার 🤣🤣🤣,0,crime
বাংলাদেশ সরকার কে বলছি জেলের ভাত নষ্ট করার চেয়ে এদের কে তাড়া তাড়ি ফাঁসি দেন ।,0,crime
মুন্নির ফাঁসি চাই সরকারের কাছে আমার অনুরোধ ওকে,0,crime
খারাপদের ক্ষমতা দিলে যা হয়,0,crime
মিন্নি জরিত বুঝা যাচ্ছে । সাংবাদিকদের এক প্রশ্নের জবাবে মিন্নি বলেছিল তার স্বামী রিফাত তাকে মাঝে মাঝে কলেজ থেকে নিতে আসে । আমার প্রশ্ন হচ্ছে সেদিন রিফাত মিন্নিকে কলেজ থেকে নিতে আসবে সেটা খুনিরা জানল কিভাবে? মিন্ন যদি না জানায় ?,0,crime
ওরা কি করে সমাজের ভালো কাজ করবে কারন ও ওরা বেহায়া নিলজ্জা জুতা পিটা করে বহিষ্কার করা হোক,0,crime
আমি একটা জিনিস বুঝি না তারা তাদের পার্সোনাল ভাবে যা খুশি করছে মানুষের এত্ত চুলকানি কেন একজনের সম্পূর্ণ পার্সোনাল বিষয়ে নাক গলানোর যারা যারা লাফাইতেছে তারা কি বুকে হাত হাত দিয়ে বলতে পারবে জীবনে কোনোদিন সানিলিওনের ভিডিও পর্যন্ত দেখে নাই,0,crime
বিচার,0,crime
আমি চিৎকার করে কাঁদতে চাইয়া করতে পারিনি চিৎকার?,0,crime
বাংলাদেশে উচ্চ পদে যারা কর্ম রত তাদের বেশি ভাগেই চরিত্রহীন,0,crime
আল্লারে আমার এত মজা রাগে কেরে,0,crime
এখন আল্লাহর গজব হরবে ওই সময় কি একটু ও কষ্ট হয় নাই নুসরাতের জন্য,0,crime
ঐ নারীকে ও কোন চাড় নাই,0,crime
এবার বুঝতে পারছেনতো কারা দেশ চালায়। কাদের হাতে এই সোনার বাংলা। হাইরে জাতি।,0,crime
যদি তুর রিপাতকে মন চাইছিল না তখন ছেড়ে চলে গেলি না কেন কেন তার সাথে মিত্যে অভিনয় করলি আর তাকে দুনিয়া থেকে উঠালি তুর তো নরকেও ঠাঁই হবেনা তুই তো ঐ আকাশের মিতুর মত করলি তুর মত বিশ্বাস ঘাতকনীর ফাসি হউক যদি রিফাত তোকে ফেলে চলে যেত তাহলে হয়তবা বেঁচে যেত সরল ভালবাসাকে হত্যা করলি তুই নারী জাতের কলংক তুকে দেখলে বুঝা যায় আসলে তোর পরিক্ষলপনা তোর চোখ মুখ সাক্ষী দেয় তুইয়ি জরিত নারী জাতের কলংক,0,crime
বাংলাদেশে চোরে আর লুচ্চামি তে কোন সমস্যা নেই । যেমন ধরুন ডি আই জি ডিসি ওসি বিচারকরা এই সব প্রমাণ পেলাম আমারা জনগণ।,0,crime
আমি তোমাকে চরিত্রহীন বলে মনে করতেছি।,0,crime
সত্য ঘটনা উদঘাটনের জন্য রিফাতের স্ত্রী মিন্নিকে গোয়েন্দা জিজ্ঞাসাবাদের প্রয়োজন আপনি ও কি তাই মনে করেন ???,0,crime
মিনিট সেঃ এর জন্য এত কিছু,0,crime
সঠিক। আমি আপনার সাথে একমত।,0,crime
রায় শুনে আমি খুশি হলাম তবে আপিল নামক মহাপ্রহসন সামনে বাকি আছে তাই একটু চিন্তিত আছি,0,crime
ফাঁসির অপেক্ষায় রয়েছি কোন সময় ফাঁসি হইবো,0,crime
ঘরের সোনা মজা লাগে না কি করবে,0,crime
বদমাস,0,crime
যে ছি ছি টিবি লাগিয়েচে তাহাকে ধন্য বাদ,0,crime
ভাই আপনে ধন্যবাদ,0,crime
সরল মনে করছে এটা কি মাপ করা যায় না বানীতে দুদক,0,crime
উপযুক্ত বিচার হোক সেটাই আমাদের প্রার্থনা এবং যারা যারা জড়িত আছে তাদেরকে সহ উপযুক্ত শাস্তি দেওয়া হোক সেটাই পাওনা ছিল,0,crime
রিফাত হত্যার সাথে মিন্নি জড়িত এই ভিডিওতে প্রমাণিত। রিফাত কে যখন ধরে নিয়ে যায় তখন সে নিরব ভুমিকায় ছিলেন। রিফাতকে কোপানোর সময় সে রুখতে চেষ্টা করেছেন। খুনিরা তার গায়ে একটি বার হাত তুলে নাই। মিন্নিকে বিচারের আওতায় না নিলে। এরকম ভাবে অনেক রিফাত হত্যা হবে। নয়নকে যে বা যাহারা সন্ত্রাসী বানিয়েছে তাদেরও আইনের আওতায় নেওয়া হোক।,0,crime
আমার কাছে মিনিটের ভিডিও আছে দেখলে দিব।,0,crime
ওর বউ সরাসরি জড়িত । ভালোভাবে তদন্ত করা হোক। বিচার চাই। ওর বউ আগেই বলেছে যারা নাকি এইটার সাথে ওরে জড়িত করবে তারা নাকি মিথ্যা আর মামলা হালকা করার জন্য বলবে আর যারা বলবে তারাও নাকি আসামিদের লোক। ? আম ার বাড়ি ঢাকা আর বরগুনা আমার বাপেও কোন দিন যায় নাই মুন্নি আসামীনি ভিডিও তেই বুঝ যাচ্ছে তুমি কতটুকু দুধে ধোয়া তুলশি পাতা। তুই নম্বর আসামি মুন্নি তোর জন্যই এত মারামারি তোর জন্যই টা ছেলের জীবন গেল।,0,crime
জ্যান্ত জালিয়ে দিলেও শয়তান দের উপর থেকে রাগ যাবে না,0,crime
ছি ছি,0,crime
মজা তুমি পাইছ আমিও পাইছি মিনিট দেখছি,0,crime
হায়রে নারি,0,crime
পালতু কথা কেন বলেন আপনি সব টা যেনে মারছেতো ওর বউ এই কথা কেন বলেন না ছিছি ছি ঘৃন,0,crime
চিঃ শুরু হয়ে গেলো কেলেংকারী!,0,crime
আজ কেনো এতো কান্না আর একটা মেয়েকে যখন মারলে তখন আল্লাহ কে মনে ছিলো না যে আল্লাহ সবার,0,crime
আল্লাহ আমাদের সবাইকে পাঁচ ওয়াক্ত নামাজ আদায় করার তৌফিক দান করুন আমিন।,0,crime
চক দিয়ে পানি চলে আসে এয় মেয়ে কারনে ছেলে কে কুপিয়ে মেরে ফেলেছে😢😢😢,0,crime
সব দোষ সিসিটিভির আর ফুটেজ এর 🤣🤣,0,crime
তার বউকে এরেশ করা হক,0,crime
এর আগে কতো বার কত নারীকে নিয়ে করছিল আল্লাহ ভাল জানে ।। জেলাশাসক ডিসি বলেই কথা,0,crime
ইসলামের আইনের আওতায় যদি এনে প্রথমে তাকে বিচার করা হতো। তার হাত কেটে ফেলত তাহলে সে আজকে এই হাত দিয়ে অন্য আরেক জনকে কুপিয়ে হত্যা করতে পারত না। দোষটা আসলে আমাদের আমরা ইসলামের আইন মানতে চাই না আবার সঠিক ন্যায়বিচার চাই। কুরআনের আইন বাদ দিয়ে মানুষ পরিচালিত আইন দিয়ে সঠিক বিচার পাবেন?,0,crime
এখনো বাকি আছে আপিল বিভাক,0,crime
যারা বলেছিলো মিন্নি নির্দোষ তারা এই ভিডিও দেখে শিক্ষা নে,0,crime
মিইয়ে টি কি হবে ভাই,0,crime
নুসরাতকে অনেক ধন্যবাদ।,0,crime
চুমা চুমি ডট কম যে যত খুশি গুষ্টি উদ্ধার করুন। দুটোকেই বিয়ে পড়িয়ে দিন।,0,crime
মেয়র মহোদয় কি করতেন,0,crime
এই হত্যাকান্ডে আমার সবচেয়ে অভাক লাগছে। মেয়ে হয়ে কিভাবে অন্য মেয়েকে মারার জন্য সাথায্য সহযোগিতা করে।,0,crime
একটু চাদ মুখ খানা দেখার সুযোগ করে দেওয়া হোক জে বিডিওটার পরিচালক অনেক সালাম তারে আমার পক্ষ থেকে,0,crime
ধুর ডিসি সাব কি বাল করলেন শুধু গাও ডা মাখালেন 😁😁,0,crime
সরল মনে ডিসি সাহেব ও মেয়েটির সাথে যৌন কাজে লিপ্ত ছিলেন এতে দোষের কিছু নেই,0,crime
এদের প্রকাশ্সে ফাঁসি চাই,0,crime
খুনিদের বিচার চাই 😰😰😰😨,0,crime
সালাম ভাই এই খুনের সাথে মেয়েটাও খুব ভাল ভাবে জরিত তাকে আগে ধরার জন্য প্রবাসীরা খুব জোরালো ভাবে অনুরোদ করছি,0,crime
এই ভিডিও তে থেকে কেন? মাঝের মিনিট কাটা কেন? রিফাত হত্যা মামলায় মিন্নীর হাত কতটুকু ? মিন্নী এক জন শিক্ষিত মেয়ে হয়ে টা বিয়ে করে এটা কি বাংলাদেশ আইনের খেলাপ কাজ না ? চাপের মুখে বিয়ে করলেও সে কেন আইনী পদক্ষেপ গ্রহণ করেনি? সব অপরাধীরই শান্তি হওয়া উচিত যা থেকে আমাদের বোনেরা বড় শিক্ষা নিতে পারে যেন তাদের কারণে আর কোন বন্ড না জন্মায় আর কোন ভাইয়ের রক্ত না ঝরে,0,crime
আমরা অবশ্যই চাই অপরাধি রা শাস্তি পাক কিন্তুু কিচু ঘটনা এমন ও হয় মুসলিম মেয়েদের চলাফেরার কালচার ভেংগে পশ্চিমাদের স্টাইলে চলাফেরা করে এতে পুরুষ তো ইভটিজিং করবেই আবার ওরাই রাস্তায় নেমে বলবে অপরাধিদের শাস্তিি চাই আমি বুঝাতে চাচ্চি দুনিয়ায় এমন একটা পরিস্হিতি বিরাজমান যে খোসা বিহিন কলা রাখা হবে অথচ মাছি বসতে পারবেনা,0,crime
সকল অপরাধী কে আইনের আওতায় আনা হোক,0,crime
রিফাত কে যখন খুনিরা দরে নিয়ে যাচ্ছে তখন মিন্নী কিন্তুু বাদা দেয় নাই বিডও তে তাই দেখা যাছে মিন্নী খারাপ মেয়ে,0,crime
ছি ছি ছি এই সব কি জুতোর মালা দিয়ে দেশের ভীতর ঘুরানো দরকার,0,crime
যারা সন্তানদের মায়ায় কান্না করতেছে তাদের মায়ার চেয়ে উচিৎ বিচার ন্যায় বিচার প্রতিষ্ঠিত হওয়া দরকার সুতরাং ফাঁশি চাই।,0,crime
চালাও ভাতিজা,0,crime
বাংলাদেশ মুক্তির জন্য কত মা বোনের ইজ্জত নষ্ট হয়েছে আর সেই মুক্তিযোদ্ধা ক্লাব নাম দিয়ে তার ভিতরে অশালীন কাজকর্ম ।ঐ ক্লাবের চেয়ে চোর মামা অনেক ভালো ।যে দল যখন ক্ষমতায় আসবে সেই দলের নাম ভাঙ্গিয়ে সুবিধা হাসিল করবে । আসলে এদের কোন দল নেই ।সবশেষে প্রশাসনকে বলবো আপনাদের অস্ত্রের গুলি কি শেষ হয়ে গেছে ?,0,crime
অপরাধিদের কোন রকম সোজগ দেওয়া হবে না,0,crime
তারা কিসের ডিলার,0,crime
তার বিচার চাই,0,crime
মাশা আল্লাহ হিজাব কিন্তু ঠিক আছে।,0,crime
মিথ্যাবাদি মহিলাটা নিজেই ছড়ায়ে ধরতেছে সে কি সত্যি কথা বলবে মেয়েটিকে রিমান্ডে নিলে সত্যি কথা বের হবে। চোরে কখনও চুরি করছে সেটা শিকার করেনা।,0,crime
এই সব মানুষেদের ফাসি হওয়া উচিত,0,crime
আরে এই মেয়ে প্রত্যক্ষ ভাবে জড়িত।সব অজুহাত বানিয়ে তৈরি করে রাখছে।,0,crime
আমার খারাপ লাগেনি অমানুষের কান্না দেখে একটা মেয়েকে আগুনে পুড়িয়েছে যখন তখন মেয়েটার আরো বেশি কষ্ট হয়েছে,0,crime
পালতু মাত বন্দু করুন আপনি।,0,crime
মেয়েটা অভিনেত্রী,0,crime
কতো খুসি কারন এখন কতকিছু হবে বলে।,0,crime
কই কি দোদের দোয়া তুলসি পাতা,0,crime
জামাল পুরের সুনাম,0,crime
মিয়া খলিফার চাচাতো বোন,0,crime
ধন্যবাদ,0,crime
কি বলি মুখে কথা নাই। এতো মানুষের সামনে ঘটনাটা হলো কেউ।এগে এলো না ছি ছি মানুষ নিজের ভাই যদি হতো তাহলেও কি ওরা সবাই এমনটা করতো,0,crime
এই ভিডিওতে আমরা জা দেখতে পেয়েছি এটা কি দেশের শরকার দেখছেনা আর জদি দেখে থাকে তাহলে প্রধানমন্তি কাছে এটায়ি দাবি করি মিন্নিকে গ্রেপ্তার করা হোক,0,crime
মিন্নী নিরদ্বোষ,0,crime
এত সব কিছু দেখেও এদের এখনও ফাঁসি দিচ্ছে না কেন আইন আইন কি অন্দ যা মানুষ বলে মিন্নির জামিনে বের হয়ে এসেছে কয়েক দিন পরে শুনবো বাকি খুনিরা ও বাহিরে হারে আইন,0,crime
সরকারি আমলারা নারী আর চুরি নিয়ে ভেস্তে থাকে,0,crime
অনেক সুন্দর বিচার হয়েছে।সকল আসামির জে দিন ফাসি হবে ।সেই দিন আমরা সকল বাংগালী শান্তি পাব,0,crime
আমার চ্যানেলে সবাই ঘুরে আসিও,0,crime
এদের যেনো তারাতাড়ি ফাঁসি হয়,0,crime
ঐ মেয়ে কেও সবার সামনে আনা হউক ।,0,crime
এই অপরাধী গুলার ফাঁশি কার্যকর হলে পরে ন্যায় বিচায় প্রতিষ্ঠা হওয়ায় শুকরিয়া আদায় হিসেবে এই শহরের বাংলা মসজিদে ইউরো দান করবো ইনশা আল্লাহ।,0,crime
যখন আপনার সন্তান শুনবে আপনি খারাপ ছিলেন তখন আপনার সন্তানই বলবে যে তোর মত মা আমার দরকার নাই ছি ছি ছি আপনার লজ্জা করো না,0,crime
ভিডিও কে করলো এটার বিচার না চেয়ে নিজের কি বিচার হবে এটা জাতি দেখতে চায়,0,crime
আমি এর তিব্র নিন্দা জানাই এবং এর সঠিক বিচার করা হউক।,0,crime
আহ ভালবাসা,0,crime
আমি জ্ঞান হারাবো মরেই যাবো বাচাতে পারবে না কেউ,0,crime
অনেকে করছে যে এতগুলো লোকের সামনে মাত্র দুটো রাম দা দিয়ে কোপালো। এখানে দুটো রাম দা এর পিছনের প্রশাসনিক শক্তিকেও গুনতে হবে। এলাকাবাসী তো দেখেছে কি ভাবে বাহিনী বারবার ছাড়া পেয়েছে।,0,crime
যেমন কাজ এমন বিচার,0,crime
কঠিন বিচার চাই,0,crime
এত গুলা মানুষের সামনে এই মারতেছে সবাই দেখের। বিবেকহীন সমাজে আছি আমরা,0,crime
ভাই দ্রুত কথা বলা শিখুন,0,crime
অপরাধীদের সরাসরি ক্রস ফায়ারদেয়া হোক! আর মিন্নিকে তার সব চলনার থেকে বের করা হোক! ~অনাকাঙ্খিত ভালোবাসা যদি মিন্নির মনে না থাকে ঐ খুনির জন্য তাহলে ভালোবাসার স্টাটাস কাকে নিয়ে দিয়ে ছিলো মিন্নি? সেটা ও কি কোন হ্যাকিং ছিলো??? নাকি সেটাও জোর করে দেয়া হয়ে ছিলো! এতোই যখন তার জীবনে সমস্যা তাহলে কেন সে রিপাত কে বিয়ে করতে গেলো! তার জন্যইতো আজকে রিপাত পৃথিবী থেকে বিদায় নিলো! খুব খারাপ ভাবেই!,0,crime
কনো কথা চলবে না তদন্ত চলবে না ফাঁসি চাই ফাঁসি,0,crime
এখন কেন কাদেন একটা মেয়েকে যখন অন্যয় ভাবে পুরিয়ে মারলো তখন মনে ছিলো না,0,crime
পুলিশের কাজে বাঁধা দেওয়ার কারণে এদেরকে জরিমানা করা উচিত,0,crime
আজকে নাস্তিক কের বাচ্চা রা আজ কই রয়ল মাতায় টুপি মুখে দারী তাকলে নাস্তিক কের বাচ্চারা আজ টকসু করতু আমাদের চ্যানালটি সাবস্ক্রাইব করুন,0,crime
এর মদ্ধে আমি কিছু বলতে চাই না,0,crime
ধন্যবাদ সরকার কে৷ আমদের৷ নেতি,0,crime
মসজিদ মাদ্রাসার কেউ হলে বিচার হত সরকারি দলের লোকের কিছুই হবেনা।,0,crime
মিন্নিও এই ঘটনার সাথে জড়িত আছে।,0,crime
লীগ বিনা ভোটের সরকারে আসে। এখন এই সরকারের আমলা আর কত ভাল হবে। তবে এটা তারেক জিয়ার চালাকী হতে পারে লীগ এমনই বলতে পারে।,0,crime
ভাই দুজনকে মেডিকেল চেকাপ করলে ধরা পরবে কিনতু বাংলাদেশের আইন তা করবেনা। সব জায়গায় মামা চলে।,0,crime
আরো,0,crime
এক মত এরকম কিছুই ঘটেনি,0,crime
নিজেও বাঁচতে চায় আবার বলে স্যারের কোনো দোষ নেই তাহার মানি কি উনি মিথ্যা বলতেছে আথবা কোনো চাপের মুখে আছে এটা আমার বিশ্বাস বাকীটা মিডিয়া গুলো তদন্ত করে দেকবে,0,crime
সব কিছু পমান আছে আর কি লাগে,0,crime
যেমন করম তেমন ফল,0,crime
স্যারের কোন দোষ নাই 🙄 যত দোষ নন্দ ঘোষ এটাই এখন চরিত্র দোষ 😠😠😠,0,crime
ফালতু ভাই,0,crime
স্ত্রী এর সাথে জরিত সন্ধেহ জনাক,0,crime
হে আল্লাহ তুমি আমাদের বাংলাদেশ থেকে রক্ষা করো এইসব খারাপ বাজে পর্ন ভিডিও থেকে।।।,0,crime
বাংগালী বিবেক দেখলে তাদের মূখে হিসু করতে ইচেছ করে আচছা সাধারণ শ্রমিকরা কি দোষ করল?আমি মালেশিয়া এরকম ক্যাসিনো দোকানে ছয় সাত বছর চাকরি করছি আমরা জানি এটা অবৈধ অনেকে ধরা পড়েছে তবে বাংলাদেশে পুলিশ প্রসাশন মত বাজে ব্যবহার করেনা এখানে দেখছি জোড় করে মহিলা মূখটা দেখানো চেষ্টার করছে এগুলো কি?,0,crime
সে এখনও সাহস করে বলেছে যে এটি অন্যের দোষ এবং তিনি যা করেছিলেন তা কোনও অপরাধ নয় আসলে আমাদের দেশের অবস্থাও এরকম যে ক্ষমতায় থাকে সে নির্লজ্জ এবং যে কোন কিছু করার সাহস করে। তারা ভাবেন না যে তারা কারও বা লোকের কাছে দায়বদ্ধ।,0,crime
মিন্নির হাটা চলায় বুজায় ও জরিত এতে কোনো সন্দেহ নাই,0,crime
আহারে না জানি মেয়েটার উপড় কতো হুমকি ধুমকি দেওয়া হয়েছে।,0,crime
মেয়েটা দুসি,0,crime
আসো খেলবো খেলা হবে,0,crime
তাড়াতাড়ি ফাসি দিয়ে মর তুই মরে জামালপুর কলঙ্কমুক্ত কর,0,crime
ভিডিও লিংক টা চাই,0,crime
এই বাঙালিরাই কি এ জীবন দিসিল? দেশকে বাচাতে?,0,crime
লোকটারে ভিলেন রাজিবের মতো লাগে।।,0,crime
ভাই আপনি দাড়ি টুপিকে সম্মান করেন তাই আমি আপনাকে সম্মান করি।স্যালুট ভাই আর ডিসি নিয়ে একটি টকশো করার জন্য একটি ভিডিও বানান।,0,crime
চুরের মায়ের বড় গলা,0,crime
এগুলা সব মিন্নি করেছে মিন্নির বুদ্ধিতে সব কিছু হয়েছে,0,crime
মিন্নি রে ফাঁসি চাই,0,crime
আওয়ামী লীগের নেতাদের এতো বেশি কেনো এই দলের নেতাদের মধ্যে ভালো মানুষ আছে কি,0,crime
ভাই এই কারণে কুমারি আইন বাতিল করছে,0,crime
মেসেজে দেখতে পাচ্ছি মিন্নি শরিফ দিয়ে প্রফাইল অর্থাৎ রিফাতের পদবী শরীফ তার মানে মিন্নি রিফাতের স্ত্রী থাকা অবস্থায় চ্যাটিং করছে নয়নের সাথে। অর্থাৎ মিন্নি রিফাতের স্ত্রী থাকা অবস্থায় নয়নের সাথে পরকিয়ায় জড়িত ছিল।,0,crime
সাধারন মানুষ করলেই ধোস,0,crime
আল্লাহ আকবার বাংলাদেশ কুথায় চলে গিয়াছে মনে হয় আবার পেরাউনের যুগ চলে এসেছে,0,crime
তাহলে কি আমাদের দেশে এখন আমরাই জিম্মি সবাই দারিয়ে দেখল কেউ প্রতিবাদ করলনা এমন হতে তাকলে পরা দেশই শন্ত্রাশের কারাগার হয়েযাবে,0,crime
ডিসির কি ভাবে চাকরি এখন আছে,0,crime
হায়রে দেশ হায়রে পুলিশ।মেয়েটাকে দেখানো হক দেখি তার চয়েসটা কেমন,0,crime
ওরত জীবন পেরত নেওয়া দরকার।,0,crime
এরকম নারী জাতীর জন্যই আজ সমাজ কলঙ্কিত। বাংলার মানুষের বিবেক দিনদিন লোপ পাচ্ছে।,0,crime
ভান ধরছে মুগুর চালান দিলেই হইতো,0,crime
পাসি চাই,0,crime
তাকে রিমান্ডে নেয়া হোক গরম ডিম দিলে সবই বের হবে!আমার জুরদার দাবি তাকে বিচারের আওতাই আনা হোক!!!,0,crime
ক্রসফায়ার করে দেওয়া উচিত জন সমক্ষে,0,crime
চোর,0,crime
রিফাতকে আল্লাহ জান্নাত নসীব করুন।,0,crime
মিন্নির হাত আছে। দরে নেওয়ার সময় সাভাবিক ছিল। মারার সময় সাভাবিক ছিল। কোপানর সময় ফিরাইসে,0,crime
এখানে কিসের তদন্ত ভিডিওতে প্রমাণ মিলে,0,crime
এদেকে ধরে রিমান্ডে নিওয়া দরকা,0,crime
আমার বন্ধু গান গায় কোকিলের সুরে তোমার বন্ধু গান গায় কুত্তার সুরে,0,crime
খুনি মিন্নির সাপোর্ট করে নারীবাদীরা এটাই প্রমান করলো এদেশে পূরুষাধিকার বলতে কিছুই নাই।,0,crime
ভাই পুরাটা ভিডিও টা এখনো দেখা হয়নি মিনিট এর ভিডিও টা থাকলে লিংক টা দিয়েন ✌✌,0,crime
ওর তো কিছু হবেনা কিন্ত যে আপলোড দিছে তার তো খবর আছে,0,crime
কানের পর কসে চর দেন একটা,0,crime
কলা,0,crime
হাই হাই,0,crime
ভিডিওটি দেখে বোঝা যাচ্ছে মিন্নিই । রিফাতা হতার প্রথম আশামি। কারণ কোন স্ত্রীর সামনে তার স্বমীকে জোরকরে ধরে নিয়েগেলে ওভাবে দারিয়ে দেখেনা ।,0,crime
এতের কথা রাইট এই মেয়ে এতে জরিত,0,crime
মাথায় কি ঠাডা পড়েছে নাকি 😂😂😂😂😂,0,crime
তাহলে আপনে একবার অনুভব করেন এই শয়তানেরা যখন নুসরাতের গায়ে আগুন দিয়ে ছিল তখন নুসরাতের কেমন লেগেছিল বলেন,0,crime
এইটা কি বাংলা মুভির সিন নাকি পুলিশ আইছে ঘটনার পর। এই বান্দির বাচ্চারা এতে জড়িয়ে আছে তাতে কোনো সন্দেহ নাই।,0,crime
আপনার কথা ঠিক,0,crime
সব ছি ছি ক্যামেরার দোষ,0,crime
রিফাত হত্যার বিচার চাই মিন্নি সহ,0,crime
মায়েরা বলে আল্লাহ বিচার করবে করতেছে,0,crime
নুসরাতের বাবা মাও একদিন এভাবেই কেঁদেছে নুসরাত হত্যার আসামিদের প্রত্যেকটা ফাঁসি চাই,0,crime
লাশ দেখতে চাই,0,crime
জুতা পিড়া না করে আজো জামাই আদর করে কেন দলিয় লোক বলে,0,crime
মিন্নির পাশের বাসার এক মেয়ে নিজে বলছে মিন্নির সব দোষ! ও মূলত এক পতিতার বেশ্যার থেকেও খারাপ ছিলো আর যে মেয়ে বলছে সে মেয়ে পটুয়াখালী পৌরসভায় কাজ থাকে এবং পড়াশোনা করে!কিন্তু মেয়েটির বাসা বরগুনা!আমি নিজেই শুনেছি,0,crime
ডিসিকে সাধারন মানুষের কাছে ছেরে দেওয়াহোক তাহলে আসল বিচার হবে সরকারি কর্মকর্তাদের উপর আমাদের আস্থা নেই।,0,crime
হতভাগা ছেলেটা জানতেও পারলোনা তারি ভালবাসার মানুষ টা এর পেছনে ছিলো,0,crime
ছলনা ময়ি নারী,0,crime
কমেন্ট সেকশানে কমেন্ট পড়ে মনে হল সবাই দুধে ধোয়া তুলসী পাতা৷ গোপনে সবাই আকাম কুকাম করে কারও প্রকাশ হয় আর কারও না৷,0,crime
অপরাধ করার সময় এক বার ভাবিসনি উপরে একজন বসে আছে সে সব দেখছে।,0,crime
জরিত মিন্নি,0,crime
মা বোনদের কথা বলে বলে মেয়েদেরকে আর পশ্রয় দেওয়া চলবে না হাতের আঙ্গুল পাঁচটা এক সমান হয় না বর্তমানে মেয়েরা আটা ময়দা মেখে একসাথে দশটা করে ছেলে পটায় এদের উচিৎ বিচার হওয়া দরকার,0,crime
মহিলা টা কে সবার সামনে উপস্থাপন করা হোক জাতি উনাকে ভাল ভাবে দেখতে চাই কারন কিছু বাকি ছিল দেখার।,0,crime
মিন্নি দাই,0,crime
এটা মোটেও এডিট করা না আমি,0,crime
এই পাপের এক অংশভাগ হাছিনার,0,crime
চালিয়ে জাও,0,crime
দেশে খুন ধর্ষন বেড়েই চলছে এইটা কিন্তু আওয়ামিলীগ সরকার এর উন্নয়ন,0,crime
আমারা ফাঁসি হলেই খুশি,0,crime
সঠিক বাবে তদন্ত নিলে দেখা জাবে সব গুলো কাজের সাথে পুলিশ ঝরিত,0,crime
পরিবার এর কোন দোষ ছিল না কিন্তু কি করার দোষ করলে দোষীর সাথে সাথে তার পরিবার কে ভুগতে হয় খারাপ লাগছে নুসরাত এবং এই পরিবার জন্য,0,crime
ভাই কারো কাছে কি ভিডিওটা হবে থাকলে প্লিজ লিংকটা দিবেন,0,crime
কারেট,0,crime
এসব ভিডিও না বানিয়ে ভিক্কা করি পয়সা কমানো ভালো ।,0,crime
ঠিক বলছেন ভাই,0,crime
এই মেয়ে ঘটনার সাথে জড়িত আছে এই মেয়েকে আগে ধরেন তার পরে সবি বেরিয়ে আসবে,0,crime
ভাই এই ফুটেজ দেখে কি মন হয়না। মিন্নি নামের খানকিটা আসল আসামি,0,crime
অভিনয় সব অভিনয়,0,crime
কান্না করে লাভ কি আপনাদের মতোই তো আরেকটা মায়ের বুক খালি হয়েছে খুব দ্রুত ফাঁসির হোক তাহলে আমাদের বোন নুসরাতের আত্মা শান্তি পাবে,0,crime
ঢুকিয়ে দে,0,crime
রতনে রতন শুয়রে চিনে কচু,0,crime
ঐ নারির ও বিচার করা দরকার তাহলে অন্য নারিরা সটিক বাবে চলবে,0,crime
রিফাত হত্যার ভিডিও তে দেখা যাচ্ছে অর স্ত্রীর হাত অজ্ঞাওজ্ঞি ভাবে জড়িত আশা করব অকেও সাস্তির আওতায় আনা হবে ইন্সাল্লাহ,0,crime
এই ভিডিও তৈরি করে কি বুঝাইতে চাইছেন? আন্ধার ঘরে সাপ । মানে পুড়ো ঘরেই সাপ। মদ গাঁজা খেয়ে ভিডিও তৈরি করলে দেশের দশের জুতার উপহার কপালে জোটবে । ঘটনার সাথে কি বুঝাইতে চাইছেন । জাতির কাছে ক্ষমা চেয়ে পুনরায় তদন্ত করে মিন্নীর চরিত্রের দৃশ্য টা ফুটিয়ে তুলতে অনুরোধ করলাম ।,0,crime
দেশটা কি মগের মুল্লুক? দেশের শতভাগ মানুষের দাবি দিবালোকে রিফাত হত্যার দৃষ্টান্তমূলক শান্তি এবং বন্ড বাহিনীর আশ্রয়দাতাদের বিচারের আওতায় নিয়ে আসা।,0,crime
হায়ৱে মুসলমান ।একটি মানুষকে মেৱে ফেলছে মানুষ সবাই চেয়ে দেখছে।ধিককাৱ জানাই এই সকল মানুষ কে।সবাই যদি এগিয়ে আসতো কুকুৱেৱ বাচচাৱা পালাইতো।ছি ছি ছি এই মানুষগুলো কেমন একটি মানুষ কে বাচাতে পাৱলো না।সবাই মজা দেখে।আমি মনে কৱি এখানে যাৱা ছিল সবগুলোৱে দশ বছৱ কৱে জেল দেওয়া হউক।,0,crime
ওদের লজজা বলতে কিচু নেই,0,crime
যাক দেশে তাহলে অাইন নামক জিনিস আছে এখনো,0,crime
হায়রে দালাল মিডিয়া! এত সুন্দর ভিডিও ফুটেজ থাকা সত্ত্বেও তদন্ত করবে! তদন্তকারী অফিসার সে নিজেই! মানুষকে এত বোকা ভাবো তোমরা জনগণ কিছু বোঝে না তাই না!,0,crime
ভিডিওটি সম্পূর্ণ সত্য,0,crime
রিফাত কে কোপানোর পর রিফাত তো নিজে হেঁটে একা রিকশায় চলে গিয়েছিলো কাহিনী মিলেনি,0,crime
এরা হচ্ছে যুদ্ধের পক্ষের শক্তি। আমি এবার ছবি বানাবো “ক্যাসিনো এটাক”,0,crime
অপরাধি এর সত্যতা প্রমাণিত হওয়াতেও আবার তদন্ত কিসের। তদন্ত মানেই অপরাধী কে নিদেষ প্রমানিত করার একটা পায়তারা,0,crime
এই হত্যার সাথে জড়িত আছে মিন্নি কোন সন্দেহ নাই আমি ভিডিওটি সমপর্ন দেখালাম তাই এমনি মনে হলো কারন আমার সবাই দেখেছি যে মিন্নি তার স্বামীকে বাঁচাতে চাইতাছে বাট সেটা অনেক পরে যখন মিন্নি দেখলো বেপারটা খুব চিরিয়াছ তখন সে তাকে বাঁচাতে আসলো এটা ওরই প্লেন চিল,0,crime
এরা ভাবে মানুষ পাগল মানুষ কিছু বুঝে না।,0,crime
সবার ফাঁসি,0,crime
হে আল্লাহ আমাদের সবাইকে অপরাধী জগত থেকে হেফাজত ফরমান এবং দন্ডপ্রাপ্ত আসামীদের পরিবারকে সবরে জামীল দান করুন।,0,crime
এই ধরনের ডিসিকে জুতার মালা পরিয়ে বাংলাদেশ ঘুরানো হোক,0,crime
বালের আইন চাকরি থেকে বরখাস্ত করলে ঠিক আছে তাহলে এসব অপরাধ কম হবে।,0,crime
বাংলাদেশের আইনে সম্মতিতে শারীরিক সম্পর্ক অপরাধ নয়। যেহেতু অপরাধ সংঘটিতই হয়নি বিচারের প্রশ্ন আসবে কোত্থেকে। তবে ইসলামী আইনে এটি মৃত্যুদণ্ডে দন্ডনীয় অপরাধ।,0,crime
এসব চরিত্রহীনেরা এভাবেই বিশেষ মিটিং করেন।।,0,crime
অন্যায়ের বিচার ঠিক আছে,0,crime
ঘটনার সাথে মেয়েটা জড়িত কিন্তু মেয়েটা বুঝতে পারে নাই রিফাত মারা যাবে মেয়েটা ভাবছিল হয়তোবা হালকা কিছু মারধোর হবে,0,crime
সমস্যা নাই কারন আওয়ামীলীগের সরকারতো তোমাদের কিছু হবে না।তোমরা আরো পতিতার সম্মান পাবা দুজন।সরাসরি ভিডিও দেখা যাচ্ছে তারপর বলছে এগুলো মিথ্যা ।যে করছে তার শাস্তি দাবি করো।তোমার জয় হবে কারণ পুলিশ সরকার সব এখন অন্যায়ের বন্ধু,0,crime
এসি রুমে থাকে ডিসি সিসিটিভি করল দোষী ধিক্কার দিচ্ছে দেশবাসী !!!!!,0,crime
পরকীয়া দুনিয়াটা চলে গেছে,0,crime
তোমার মা মারা যাবে যদি এইটা এরিয়ে জাও লা ইলাহা ইল্লাল্লাহু মুহাম্মাদুর রাসুল্লুলাহ এইটা জনকে দাও।কিছু করার নাই আমাকেও জন এ দিছে পরিস্থিতির শিকার। কারন আমি আমার মাকে অনেক ভালোবাসি,0,crime
গুজব!,0,crime
যতই মেয়েটারে খারাপ বলি পৃথিবীর সকল মেয়ে খারাপ সকল ছেলে খারাপ আবার তা না কিছু কিছুর জন্য দুনিয়া নষ্ট কিছু কিছুর জন্য আখেরাত আমাদের মুখে কারো সত্য কথা না ইউটিউব চালাই আমাদের মুখে কারো সাথে কথা নাই বিচার করি আইন করি একদিন বুঝবে যেদিন আজরাইল হাত পায়ে কড়া করে ভাবে রশি দিবে যেমন করে মুন্নির স্বামীকে মৃত্যু করেছিল মৃত্যু যে কত ভয়ঙ্কর,0,crime
ভিডিওর লিংক কই,0,crime
তিনি আওয়ামী লীগ করেন।এটা কোন ঘটনাই না।,0,crime
আমার ভাবতেও গিনা লাগে যে এই আমাদের বাংলাদেশ এতো গুলো মানুষের সামনে কিভাবে একটি ছেলেকে এবাবে কুপিয়ে হত্যা করে,0,crime
আমি প্রশাসনকে দৃষ্টি আকর্ষণ করে বলছি মুন্নিকে ধরেন ওরে রিমান্ডে দেন সব বের হয়ে যাবে কারণ ও রিফাত শরীফ হত্যার সাথে সিওর জড়িত আছে!!!,0,crime
অনেকে বলে সে চাকরির কারণে বাধ্য হইসে এইগুলা করতে কিছু দুর্নীতি ঘুষখোর রা বলে তারা নাকি এগুলা নিতে বাধ্য হয়। আমি বলি এখন এইটাই সমস্যা। সবাই চাকরি যাবার ভয়ে সকল অনৈতিক দাবি মেনে নেয়। এইটা কোনো যুক্তিযুক্ত কথা হতে পারে না। চাকরি গেলে আপনি অন্য চাকরি করবেন আপনার যোগ্যতা থাকলে আপনি অবশ্যই চাকরি পাবেন ই। তাই আপনি নিজে সৎ হোন তাহলেই হবে। এখন চাকরির ক্ষেত্রে অন্যতম বড় গুণ হল বস এর গুনগান করা তেল দেয়া ইত্যাদি। মানুষ এর আত্মসম্মান না থাকলে এগুলা কখনো দূর হবে না। যারা বলে তারা বস এর কারণে বাধ্য হয়ে এগুলা করে তারা মিথ্যাবাদী খারাপ। আপনি না চাইলে কেউ আপনাকে জোর করে কিসু করাইতে পারবে না।,0,crime
আরে ভাই আসল খুনি মিন্নি। যে ভাবে অভিনয় করতাসে তাতেই পুরা মিন্নি আর তার সহ কারি দের ফাসি দেওয়া উচিত। জাতে কেও এই রকম না করে।,0,crime
মানুষ কি বোকা কোনটি ফেক কোনটি ইডিড করা বুঝে না। সরকারি কর্মকর্তা কোন না কোন কুকাজ করেই সেটা এমন না হয় দূর্নিতী ঘুষ জুলুম ইত্যাদি না করে কি করবে সরকারি কর্মচারীরা এসব করতেই পারে অপরাধ নয় তাদের জন্য সবই বৈধ,0,crime
লা হাওলা ওয়ালা কুওয়াতা ইল্লা বিল্লা আল্লাহ্ তুমি এদেরকে হেদায়েত দান করো আর যদি তাদের কপালে হেদায়েত না থাকে তাহলে তাদেরকে দংশ করে দাও,0,crime
এই ভিডিওতে যারা ডিসলাইক 👎দিচ্ছে তাদের ধরিয়ে দিন।,0,crime
কি বলবো ভাষা হারিয়ে ফেলছি,0,crime
বর্তমান দ্বায়িত্বে যারাই আছে তাদের চরিত্র নিয়ে সন্দেহ হয় হাই রে ডিসি,0,crime
এই মেয়েটিকে আইনের আওতায় নেওয়া হোক,0,crime
পাপ করার সময়ে মনে ছিলানা এই কথা,0,crime
বাংলাদেশ কামরু কামাইক্ক্যা হোয়েগেছে সুতরাং হিন্দুর মুসলিম সমাম সমান,0,crime
খুব কষ্টকর এরা কেন এসব করল মা বোনের কত আহাজারি,0,crime
আজ যদি না হয়ে মসজিদ মাদ্রাসার ইমাম অথবা শিক্ষক হত তাহলে চেতনাশীলদের জ্বালায় আর থাকা যেতনা ।,0,crime
এটার চেয়ে মিন্নী আর নয়নেরটা ভালো ছিলো। কিছু টা হলেও বোঝা গেছে। এইটা তেমন বোঝা যায় না সালাগো টাকা হইছে কিন্তু আত্মা হয় নাই। ভালো একটা ক্যামেরাও নাই😁😁,0,crime
প্রথম দেখলাম,0,crime
মান সম্মান শেষ!!,0,crime
গ্রামের লোকদের কথায় যা বুঝলাম রিফাত কে খুন করিয়েছে ওর বউ মিন্নি নয়ন নামে ওই কুত্তার বাচ্চার সপ্তাহের মধ্যে গ্রেপতার করে ফাঁসিতে ঘুলিয়ে মারা হোক আর ওর বউ পতিতা কে রিমান্ডে নিয়ে পেটানো হোক,0,crime
মিন্নিকে জিজ্ঞাসা করা হউক,0,crime
আজ আমার কাচে খুভ ভালো লাগচে কবে আবরারের খুনিদের পাসিহবে ওদের পাসি হলে আরো ভালো লাগবে,0,crime
সবাইকে আইনের আওতায় এনে উপযুক্ত শাস্তি দেওয়া হোক,0,crime
মাননীয় শেখ হাচিনা আপনার বাবা দেশ সেস,0,crime
যেমন প্রকাশহ দিবালোকে হত্যা করা হয়েছে তেমনই হত্যাকারীদের প্রকাশহ দিবালোকে ফাসি দিতে হবে।,0,crime
সরিয়া আইন বিচার চাই,0,crime
এই খুনের সাথে মিননীও জরিত। রিফাতকে কুপানোর পরে মিননী তার জুতা ও বেনিটি বেগ খুব ঠান্ডা মাথায নেওযা দেখে বুজা যায মিননী জরিত ।,0,crime
মিন্নির কাহিনী টা প্রসাশন কে খতিয়ে দেখার জন্য অনুরোধ করবো।,0,crime
আপনাকে মিন্নি কতো টাকা দিছে গানের জন্য নয়ন ও রিফাত তাদের দুইজন কে আল্লাহ জান্নাতুল ফেরদৌসের দান করুন আমিন,0,crime
এরা ক্ষমতার জোরে সব কিছু করতে পারে এরা মানুষকে মানুষ মনে করে না এদের তো শালারে জুতা দা বাইরে বাইরে তেমাথা মাথা টাক করার উচিত,0,crime
ম্যা ম্যা,0,crime
এই মহিলার নয়নের সাথে আগে বিয়ে হয়েছে তাহলে রিফাতের সাথে কেন বিয়ে করল আবার রিপ্লে কেন মারল একে রিমান্ডে নেয়া দরকার,0,crime
একটা কথা আসল দোসি কে,0,crime
ভাই সেকেন্ড পাইয়া গেছি,0,crime
কি অবস্থা,0,crime
স্বামীকে ধরে নিয়ে যাচ্ছে। মিন্নি তো বাধা দিল না। সেও অন্য দের সাথে সাথে হাটছে। তাও আবার হেলতে দুলতে।,0,crime
এই মেয়ে জরিত আছে আই হত্তার সাথে সেতা আগে এ বুঝা গেসিলো এই ভিডিও দেখার পর ত আর স্পষ্ট হয়ে গেল।।।।,0,crime
এমন জেলা প্রকাশক!!! 😊😂😆😇,0,crime
তাদের হাতে অস্ত্র ছিল তাই কেউ সামনে আগাতে সাহস পায় নাই। যদি সবাই মিলে চেষ্টা করতো তাহলে ছেলেটা মৃত্যুবরণ করত না।আর রিফাতের স্ত্রীকে ভালভাবে জিজ্ঞেস করা উচিত। তাহলে ঘটনা আরো পরিস্কার হবে।,0,crime
ঐ নারি বিশেষ সুবিধা নেওয়ায় জন্য ডিসি সামনে কাপড় খুলেছে।,0,crime
অাগাছাদের বালের ভিডিও না দেখে কমেন্ট করেছি,0,crime
ডিসি ত,0,crime
ভাল করে তদন্ত হোক।পরে বিচার হোক।অনেক সময় নিরপরাধ ও ফেসেঁ যায়।সত্যি কথা মিথ্যা প্রমাণ হয়।এখন মিথ্যার যুগ।তাই সত্যি বের করা হোক।জুলুম বেরে গেছে সমাজে।,0,crime
পরিবারের লোক আজ কানছে কানো????? তাদের যদি পরিবারের কথা মনে থাকতো তা হলে এই রকম কাজ করতে পারতো??????????? 🤔🤔🤔🤔,0,crime
ওখানে বাংলাদেশ তৈরী হয়েছে ওখানে শেখ মুজিব জন্ম নিয়েছে,0,crime
রনি কে,0,crime
ঢুকাইছে তারপরও দোষ নাই ক্য,0,crime
আমি জা দেখলাম মিন্নি জরিতো কারন ওর সামিকে নিয়ে জায় আর ও আসতে আসতে হাটে,0,crime
মিন্নিকে ফাঁসানো হচ্ছে প্রভাবশালী দের বচানোর জন্য।,0,crime
ওনাদের কাছে মানুষ গুলো কানা হয়ে গেছে আর মনে করে বোকা হয়ে গেছে,0,crime
আচ্ছা প্রথম আলোর সন্মানিত ভাইদের কাছে আমার প্রশ্ন ভিডিওটির এর অংশটুকু কোথায়???? জানি কোনো নাই আপনাদের কাছে,0,crime
যেই দেশের সরকার পরকীয়া করে সেই দেশের আইনজীবীরা কি করবে না এটা কি কথা হলো এটাতো একটা স্বভাবিক। আর বাংলাদেশের সবাই হিজড়া হয়ে গেছে আর সব কান্ড মন ভরে উপভোগ করছে। কিনতু কারো কোনো মাথা ব্যাথা নাই। আরে গাধারা দেশটা তো ধংস হয়ে যা তুমরা চাইলে সবাই এক হও দেখবে দেশটিনিয়ন্ত্রণেআসবে।,0,crime
না ঠিক আছে পতিতার দোষ নাই দোষ হইলো ভিডিও কে করছে যারা এসব পতিতার সাপোট করে তাদের নিউস করে তারাও পতিতার দালাল,0,crime
স্যারের কোনো দোষ নাই সব দোষ তাহেরির,0,crime
এইখানে সবচেয়ে বেশি অপরাধী মিন্নী। তার হাটা চলা দেখেই বুঝা যায় সেই মেয়েই ছেলেদের দিয়ে তাকে মাডার করিয়েছে।,0,crime
লুচ্চামি আর খুন করতে আল্লাহর কথা মনে পড়ে নাই,0,crime
মহিলা সুন্দর আছে। লোভ সামলাইতে পারেনাই। আল্লাহ জানে কয়টা মেয়েরে ব্যাবহার করছে,0,crime
অপরাধ করার আগে স্মরণ থাকে না 😫এবার ফাঁসির কাষ্ঠে ঝুলতে হবে।,0,crime
মরে যান।দুনিয়াটায় খারাপ মানুষ ভরা।দেখলেন না আপনাদের গোপন কাজ ফাস করে দিল।,0,crime
রিফাত হত্যায় তার বউ এর হাত রয়েছে।,0,crime
সরকারি সব দালালরা এখানে সম্পৃক্ত,0,crime
কোনো দোষ নেই একটু মজা করেছে শুধু।,0,crime
মিন্নিকে দেখা যাচ্ছে পেছন পেছন দল বেধে হাটছে,0,crime
ফাসিটা যেনো তারাতারি হয়ে যায় তাহলে সবাই আরো খুশি হবে,0,crime
স্যারের দোষ নেই সব দোষ আপনার। শরীর কে লোভনীয় রুপে সাজিয়ে আসেন অফিসে। স্যার মাতাল দেহে। দোষী কে তার শাস্তি নির্ধারণ করা হোক,0,crime
যদি এরা সবাই জরিত হয়েথাকে নুসরাত হত্যায় তাহলে বললো খুব ভালো হবে ফাসি হলে এটাও বলবো যেনো কোন নির্দষ লোকের শাস্তি না হয়,0,crime
বেশ বেশ বেশ সাবাস বাংলাদেশ যাও এগিয়ে তোমাদের পাশে আছে জনগণ তোমরা করো ও ধর্ষণ পুলিশ,0,crime
এদের যেনু খুদা প্রেছনডো 🌹🌷🌸🌺💐🏵,0,crime
ধন্যবাদ সঠিক তথ্য দেয়ার জন্য,0,crime
ডিসির লিংকও বের হয় না হায়রে গরিব বাংলাদেশ😎😂,0,crime
মিন্নি কে আগে ফাঁসি দেওয়া হোক,0,crime
কিরে ভাই ডিসি তরে কত টাকা দিলো তুই ডিসির হয়ে চামচামি করতাসছ কেনো,0,crime
সুন্দর উপস্থাপন। হাঁ হাঁ,0,crime
দয়া করে এমপি ডিসি এদের এই অশ্লীল ভিডিও লিংকটি আমাকে দেন আমি পাচ্ছিনা তাই।,0,crime
হিছা মার,0,crime
আজকে এই ভিডিও দেখেই বুঝলাম মধ্যে মিননি জড়িত । কাল্পনিক ডাইনি আর রাখ্যশের গল্প শুনেছি কিন্তু বাস্তবে দেখার সৌভাগ্য হয়নি আজ এই আধুনিক যুগে বাস্তবে মানুষ রুপি রাখ্যশকে দেখার সৌভাগ্য হলো আমিন বিশ্বের বুকে স্থান করে নিল এই নারী।যা সর্ব যুগের সেরা রাক্ষুসী নির কোনো অঙসে কমনা।এই বাঙলার জমিনে বিচার নিশ্চয় হবে আওয়ামী লীগ সরকারের আমলেই হবে । আওয়ামী লীগ এই নারী কে ফাসি দিতে না পারলে কেউ পারবেনা । ইতিহাস আওয়ামী লীগ সরকারেরই আছে ফাঁসি দেয়ার জামায়াত শিবিরের ও বিএনপি রং নাই ।,0,crime
যে কোন বড় ধরনের অপরাধের সাথ রাজনৈতিক প্রভাব রয়েছে,0,crime
যার দোষ থাকুক কুপিয়ে মেরে ফেলেছে । ইস কিরকম লাগে,0,crime
সে অপরাধী চেহারা দেখলেই বোঝা যায়,0,crime
আকাম করার সময় খেয়াল থাকে না।।।।,0,crime
কৈ পেলো এতো টাকা বেটা ?,0,crime
সাধারন পাবলিক চতুরপাশেই মরবে এ আর নতুন কি তবে খুশির বিষয় এই যে যারা এমন অবৈধ কারবার গরবে বা যারা এইসব কারবার চলমান রাখতে খমতার চেয়ারে বসে কারবারিদের মাথায় ছাতা ধরিয়ে রাখবে তারাত সব সময় সম্মানের সহিত সেভ থাকবে যেমন কম্পানি চলবে ডিস্টার্ব নকল মাল রাখার দায়ে কেবল মাত্র দোকানিই অপরাধি হয়ে আটকা পরবে । এখানে যারা জুয়া খেল্ল বা যারা নকল মাল বিক্রয় করলো তারা অবশ্যই অপরাধি তবে এদের কাছে আইনের চাবুক মারলেই অপরাধ কমবে না বরং যারা নকল মালটি বানাল যারা জুয়া খেলার স্থান তৈরি করলো তাদের যদি শাসন করার কোন পথি না থাকে তাহলে অপরাধ কমে কি করে । আইনের মুল লক্ষ হবে অপরাধি কমানোর চেয়ে অপরাধ কমানোর দিকে কিন্তু তেমন আইন প্রয়োগে আইনেরি যখন হাত বেধে ফেলেছে অপরাধ গ্রুপ অপ ইন্ডাস্ট্রিজ তখন সত্য এটাই যে সাড়া গায়ে ঘা হয়ে গেছে মলম দেবে কোথায় ।,0,crime
মেয়েটা ছিলো এক নামবার খারাপ,0,crime
তার কথা বুজা গেলো সে দসি আপনাদের কি মনে হয় আমি তো বলি সে দসি,0,crime
কোন মিল নাই,0,crime
ভাই তোমরা যাই কও আর তাই কও।আমি যে নিশ্চিত এই ঘটনা মেয়েটি সম্পর্ন ভাবে জরির্ত,0,crime
অভিনয় কি আর পাস না আজাইরা এই গুলা নিয়া মজা করস পারলে প্রতিবাদ কর,0,crime
যার সুন্দরী বৌ থাকতে সামান্য একটা মেয়ে র সাথে এসব করে সে মানুষ নামের কলঙ্ক ।আমি ভাবতে পারি নি একজন ডিসি এত নিচে নামতে পারে,0,crime
পুরো বাংলাদেশটাই আজ পতিতালয়!😢,0,crime
এরই নাম বাংলাদেশ ডিসি সাহেবের নিজের ভিডিও ডিসি সাহেব নিজেই তদন্ত করছে বাহ! কি হাস্যকর কাহিনী কিন্তু আজকে যদি এটা কোন সাধারণ ব্যক্তির হয়তো তখন ওই সাধারণ ব্যক্তিটিকে হাজতে বড়া হইত এবং মামলা করা হইত কিন্তু আমাদের বাংলাদেশ উনিতো ডিসি সাহেব হয়তো কিছুই হবেনা তার সুতরাং বাংলাদেশ আইন সবার জন্য সমান না,0,crime
আমি অনেক বার বলেছি এই ধরনের মিন্নি সংখা অনেক যার জন্য ধ্বংস হইতাছে হাজার হাজার রিফাতের মত জীবন এই যে মিন্নি,0,crime
শুধু এই ডিসি কেনো আওয়ামীলীগ এর সমস্ত উপরের নেতা মন্ত্রীরাই এমন কর্মকান্ড করে বেড়ায়।জাস্ট সেগুলো কোন ক্যামেরায় বন্দী হয়নি এখনো।😁😁😁😁,0,crime
হা হা হা হা হ্যাকের গ্রুপ,0,crime
সরকার যদি আসলে ন্যায়পরায়ন হয় তাহলে অবশ্যই এটার সঠিক তদন্ত করে উল্লেখিত ডিসির শাস্তি প্রধান করে নজির সৃষ্টি করবেন বলে জনগন আশাবাদী।,0,crime
আমরা যতই পরিষ্কার ভিডিও দিয়ে প্রমান বের করে পুলিশের হাতে ধরিয়ে দেই না কেন এসব দিয়েও বাংলাদেশের আইনি ব্যবস্থা এতোটাই ঠুনকো যে পুলিশ কখনো কোনো মামলায় আসল অপরাধীদের শাস্তি দিতে পারেনি পারবেওনা,0,crime
স্যার কোন ক্ষতি করে নাই একটু সুখ দিয়েছে আর কি।,0,crime
ভিডিওতে দেখা যায় প্রথম যখন রিফাতকে হাতে মারছিল তখন মিন্নি কিছুই বলে নাই বা থামানোর কোনো চেষ্টাও করে নাই। যখন রিফাতের উপর রামদা চালানো হল তখন মিন্নি হাত পা নারাচ্ছে। মিন্নি জরিত আছে,0,crime
একটা মানুষও গিয়ে ধরলো না।😂,0,crime
ধুর বাল ভিডিও এর লিংক কই 😄😄😄😄,0,crime
এগুলো কিসের শর্ট ফিল্ম হা,0,crime
খেলার সময় খেলতে পারো এখন বলো আমি কিছু যানিনা। যানেটা কে মজা তুমিও পাইছো আমিও পাইছি।,0,crime
গতও তিন মাস যাবত ঢ়ালতেছে তলা বিহিন বালতি ঢ়াললে কি আর ভরে !,0,crime
ভুতের মুখে রাম নাম।,0,crime
ফালতু,0,crime
পাপ ছারেনা বাপ রেও,0,crime
মিন্নি ঠিক বলেছেন সব কিছু চালাকি করছে এমপি পুত্র সুমন,0,crime
মিননি কে ফাঁসি দেওয়া উচিত,0,crime
আসল খুনি ওকে ফাঁসি দেওয়া উচিৎ।।,0,crime
এ রকম বিচার হলে মানুষ অপরদ আর করবেনা,0,crime
এত হাজার হাজার মানুষ চেষ্টা করলে মাইট্টা ফিরে দিতে পারতো কিন্তু ইচ্ছা করে নাই জানিনা কেন করে নাই ওপরে আল্লাহ জানে,0,crime
মহিলারা পুরুষ নষ্টে কম দায়ী নয়,0,crime
ফরেমেযেকেমারারপরিনামএই,0,crime
ভিডিও টি যে করেছে আল্লা তাকে হেফাজাত করুন।,0,crime
কেমন লাগে আমার বইন নুসরাত ওই দিন বাঁচতে চেয়ে ছিল তোরা বাঁচতে দিলিনা জত দ্রুত ফাঁসি কারজকর করা সমবব হে দুনিয়ার মানুষ দেখো বাংলা দেশে সুস্ত বিচার হয়ছে বাংলাদেশ,0,crime
চাকুরী থপকে বাদ দেওয়া হক,0,crime
কেউ কি খেয়াল করেছেন ? মিনিটের সময়? ?? তখন ঘড়িতে ? সেকেন্ড ছিলো। সেকেন্ডের ব্যাবধানে ? সেকেন্ড! !!!!!! অর্থাৎ মিনিট সেকেন্ড উধাও! ! কি ঘটেছিল ঐ সময়? ঐ সময়ে রিফাত মিন্নিকে ডেকে নিয়ে রাস্তার অপজিটে থাকা সাদা মটর সাইকেলে করে চলে যেতে চেয়েছিল। কিন্তু মিন্নি তার সাথে রাজি হলো না। কালক্ষেপন করে আবার কলেজের দিকে রওনা হলো। তার পরবর্তী মিনিটেই রিফাতকে ধরে মারাত্মক ভাবে মারা হলো। আশ্চর্য ব্যাপার হলো প্রথম আলো ঐ অংশটুকু বাদ দিয়েই ভিডিও টি প্রকাশ করেছে!! কিন্তু কেন????,0,crime
সরকার এখন কি করে দেখি,0,crime
চেহারার মাঝে কোন পরিবর্তন নাই নয়ন মারা যাওয়ার পর মুন্নির মন খারাপ হয়ে গেছে ও খুশি হয় নাই,0,crime
আসামীর ফাসি রায় আদালত দিয়েছে তা অতি তারাতাড়ি কারজকর করুন যা দেখে আর কেই তাদের মত অপরাধ করতে সাহস না পায়,0,crime
খুনিদের ফাসি চাই 😡😠😠😠😠,0,crime
মজা তুমিও পাইছো স্যার ও পাইছে😂😂,0,crime
ওরা মিডিয়ার সামনে কথা বলে ওদের লজ্জা থাকা উচিত,0,crime
ওকে হাফেজ কেন বলা হচ্ছে ওকে খুনি পরিচয় দেওয়াহোক,0,crime
মিন্নি জরিত এতগুলো লোক থাকতে একটি ছেলেকে কুপিয়ে যায় কি করে বাংলাদেশ বলেই সম্ভব ছি ?,0,crime
যেমন কর্ম তেমন ফল কোথায় স্বর্গ কোথায় নরক কে বলেছে বহুদুর মানুষেরী মাঝে স্বর্গ নরক মানুষেরী মাঝে সুরাসুর।,0,crime
এই মেয়েটি সব নষ্টির মুল!,0,crime
পাপ বাপকে ছাড়ে না কিন্তু যতই হোক স্বজন তো বুক ফেটে যায়।। কিন্তু কি করা এমন কুলাংগার দুনিয়াতে থাকার চেয়ে না থাকা ভালো যারা এমন করে মানুষ মারতে পারে তারা মানুষ না!!!!,0,crime
নিজের স্বামী কে জড়িয়ে কয়েক জন নিয়ে যাচ্ছে আর বউয়ে কোন ফিলিংস নাই ।,0,crime
মিন্নি র ফাশি চাই,0,crime
আরেক জন্নের জান নায়ের সময় তু অনেক কুশি চিলে,0,crime
স্বাধীনতা চাইনি আমি এই স্বাধীনতা স্বাধীনতা পাইনি আমি সেই স্বাধীনতা,0,crime
দিন দিন এসব কর্ম কান্ডের বৃদ্ধির মূল কারণ হলো তাদের প্রতি দয়া না দেখানো,0,crime
কি বিছার ব্যবস্থা এখন লুচ্চারে পুলিশে গ্রেফতার করার কথা ছিল তা না করে আবার তদন্ত করা শুরু করছে।,0,crime
তুই খারাপ মহিলা তুই যেখানে যাবি সেই পরিবেশ নষ্ট করে ছারবি।,0,crime
চিল্লাইয়া মার্কেট পাওন যাইবো 😀 এরপরও একদল লোকে বলবে আমি বালানা আমিও বলি আমিতো বালা না বালা লইয়া থাকি 😂😂,0,crime
আমি পরে কমেন্ট করবো। আমি এখন হাসপাতালে 😪😫 আমার গ্রামের চাচাতো ভাই জিবি মেমোরি গিলে ফেলেছিলো😮এখন সে সব গান গাইতেছে☺আমরা সবাই প্রার্থনা করি যাতে সে ভিডিও ফোল্ডারে না প্রবেশ করে😑🙄,0,crime
লজ্জা নাই বিষ খাইতে পারিস না তোর মা বাবার ছেলেমেয়েদের সামনে মুখ দেখাচ্ছিস কু ভাবে,0,crime
যখন অপরাধ করে তখন বাদা দিতে পারনা এখন এসব মায়া কান্নার কোন দাম নাই,0,crime
বাই যে এই ভাবে বিডিওটা করেছেন কষ্টো করে। আমরা চাই যেই কোন সময় আপনার মত করে যেন কেউ। যেন যে কোন হামলা বিডিও করে আইনকে বাদ্য করে বিচার করতে। আবার ও প্রমান হলো বাংলার মানুষ আগের মত নয়।সেলোট বাই।,0,crime
এই জানোয়রে শয়তানকে মেয়কে পুরিয় মারা দরকার জনোগনের সামনে,0,crime
ড ছি,0,crime
হাহাহা চোরের মার বড় গলা,0,crime
আমরা অপেক্ষায় আছি সবাই যেন আমরা সবকিছু যেন খুব তাড়াতাড়ি ভুলে যাই। পরে বিচার কার্য সঠিকভাবে সমাধান করা যাবে।,0,crime
ঐদিন তো নুতরাতও বাঁচার জন্য তোদের পায়ে পরেছিল তোদের একটুও মায়া লাগে নি।,0,crime
দেশে কি আইন কিছু নাই না এটা গুজব পুলিশ প্রশাসন কি বলছে একটু দেখব ভাই এটা গুজব গুজব গুজবে কান দিবেন না,0,crime
সুন্দর কথা বলেছেন ভাই 🌷👍,0,crime
আসল ঘটনা না জেনে আপনার জারি বানানো টিক হয়নি । আগে ঘটনা সম্পর্কে ভালো করে জানতে হবে তার পরে সুন্দর করে একটা জারি বানাও ।,0,crime
ব্যাপার না বস চালিয়ে যান বাংলাদেশে এগুলো এখন স্বাভাবিক ব্যাপার হয়ে গেছে,0,crime
এর পরেরটা কই,0,crime
দূর মিয়া এইগুলা ইডিট করা যায় 🚷🚷🚷🚷🚷🚷,0,crime
ওনার টা দারায় না তাই ডালতে পারে নি,0,crime
আইনের লোক হয়ে লুচ্চামী সে আবার অন্যদের বিচার করবে কেমনে ধরা খেয়ে এখন কিছু জানে না,0,crime
আমার মনে এই হত্যার সাথে মিন্নির সম্পুন্ন হাত আছে ওকে আগে গ্রেফতার করা হোক,0,crime
এদের আবার বিচার কিসের? এদের ধরে ফায়ারিং স্কোয়াডে নিয়ে ক্রস ফায়ার করা হোক😡😡,0,crime
এই মহিলার স্বামী এবং সন্তান রয়েছে। তারপরও কেন যে তিনি এসবের সাথে জড়ালেন!!!🤔🤔,0,crime
মিন্নি হলো আসল খুনি,0,crime
রিফাত কে তার বৌ মিন্নি খুন করিয়েছে মিন্নি গ্রেপ্তার করে রিমান্ডে নিলে সব তথ্য পাওয়া যাবে।,0,crime
খুব খারাপ ঘটনা ঘটেছে।,0,crime
পারলে এত মানুষ ছিল অই খানে ওরা বাচাতে পারত একটা প্রান। বিনা অপরাধ এ চলে গেছে একটা জীবন 😢আর যে এ রকম কত জীবন চলি জাবে।,0,crime
মিন্নি একি পশাকে দুই জন এর সাথে মেয়ে রা সাধারনত একটা পোসাক অতিরিখত মাশ পরে তার মানে এই মেয়ে টা রিফাত এর সাথে বিয়ে হবার পর অ নয়ন এর সাথে মেলামেসা করত তাই এর অ সাস্তি চাই,0,crime
এই যদি হয় দেশের অবস্থা তাহলে সাধারণ মানুষ করলে দোষ কি,0,crime
ওর কঠিন শাস্তি হউক,0,crime
ঘরে কারিনা রেখে।।।।ডিসি গেলো জরিনার কাছে।ছি,0,crime
কি অদ্ভুত আমাদের দেশের মানুষ তাইনা যে কিনা অপরাধকে ধংস করবে সে নিজেই অপরাধী যখন মূর্খ মন্ত্রী অথবা বজ্জাত ব্যক্তি ব্যক্তিত্বের থেকেও দামী চেয়ার পায় তখন লাত্তি দিয়া সেই চেয়ার থেকে তাকে ফেলে দেওয়া উচিৎ।,0,crime
পাপ বাপকেও ছাড়ে না।,0,crime
নিজের তদন্ত নিজেই করবেন!!!,0,crime
যেরা দেখ ছিল তারা মানুষ নয় পশু ভাই আমার মত এই মেয়েকে জেন ফাঁসি না ক্রছ ফায়ার করা হুক তাতে সব মেরা টি হয়ে যাবে একটা দেশ টিক করতে একজন কে তার প্রাপ্প সাজা দিন গেরান্টি দেশ টি হয়েজাবে,0,crime
খু‌নি‌দের বিচা‌রের সা‌থে সা‌থে যারা দার্শক ছিল অথচ রিফাত‌কে বাচা‌তে এ‌গি‌য়ে আ‌সে‌নি তা‌দেরও বিচার চাই। এটা কেমন অমানু‌ষিক আচরন। সাম‌নে একটা মানুষ কু‌পি‌য়ে মার‌ছে আর পা‌শে দা‌রি‌য়ে সবাই ইং‌লিশ মু‌ভি দেখ‌ছে ম‌নে। দু‌নিয়াতে দ‌র্শক‌দের বিচার না হ‌লেও পরকা‌লে ঠি‌কি হ‌বে। সবাই অপরাধী,0,crime
খুবই খুশি সঠিক বিচার করার জন্য,0,crime
নারী জাতির কলঙ্ক ।,0,crime
যাই হক এতোদিন পরে সঠিক বিছার হইতাছে নুসরাতের আত্মা শান্তি পাবে,0,crime
ঃ রিফাত বিশ্বাস লোকটা কে?শুনছিলাম শুধু রিফাত।এখন আবার বিশ্বাস যোগ করে দিলেন,0,crime
যমুনা টিভি আপনাদের বলছি। আপনারা বাড়ানোর জন্য যা করছে তা কি সাইবার অপরাধে পড়েনা এই মহিলাটাকে আপনারাই মানষিক নির্যাতন করছেন। আজব দেশ আমাদের।,0,crime
নিজে মরবে শুনে আল্লা বলে ডাকছে আর নুসরাত কে মারছিলো ৷নুসরাত তো বলেছিলো আব্বু চাচা ভাইয়া আমাকে ছেরে দাও ওরা কি ছেড়ে দিয়ে ছিল ৷,0,crime
এটা কোন কমেডি হলো,0,crime
ওকে সাজা দেওয়া হোক আজগে জায়গায় কোন আলেম হলে সারা দুনিয়া ছড়াই দিতো,0,crime
হায়রে ডিসি,0,crime
দেখুন ধরা খেলো ছেলে,0,crime
এই ছেলেকে আইনের আওতায় আনা উচিত।,0,crime
রক্ষক যখন ভক্ষক হয় তখন আইনের শাসন অকেজু হয়ে যায় ।,0,crime
অপরাধ ত‌ো কর‌েছে বিচার হব‌ে কি,0,crime
সকল পুরুষেরা সাবধান!!!! সারাজীবন মনে রাখবেন কথাটা শুনতে খারাপ শুনালেও সত্য শয়তান ইবলিস অস্ত্র হিসেবে ব্যবহার করে নারীদেরকে। হযরত আদম আ থেকে আজ পর্যন্ত একি ঘটনা। এছাড়াও ক্রুসেড সিরিজ পরলেও ব্যাপারটা স্পষ্ট হয়। তাই সকল নারী হতে সাবধান। নারীদের যথার্থ মর্যাদা দিন এর ব্যতিক্রম ঘটলে ইবলিস এর খপ্পরে পড়বেন। পুরা লাইফ ধ্বংস করে ছাড়বে।,0,crime
আমি মিননি জরিত,0,crime
তদন্ত করে কে কে অপরাধি তাদের সবাইকে জনসম্মুখে কোর্সফায়ার করা হক।কোন বিচারের দরকার নাই এটা আমার একান্তব্যক্তিগত কথা,0,crime
এই খুনের সাথে জড়িত অবশ্যই ওই ডাইনি রিফাত কে হত্য করা হয়েছে সব এই ডাইনি মহিলার পরিকল্পনায় তাই বলব এই মহিলার বেঁচে থাকার কোন অধিকার নেই এই মহিলা বেঁচে থাকলে আরো ওর মত মিনি জন্ম হবে তাই বলব আর যাতে কোনো ডাইনি মহিলা ওর মতন না হয় ওর কঠিন শাস্তি হওয়া উচিত এবং ওর ফাঁসি চাই আমরা কারণ ও যদি বেঁচে থাকে ওর দেখা দেখে অনেক মহিলারা তার স্বামীকে কুপিয়ে হত্যা করবে তাই চাই ওর যেন ফাঁসি হয় এবং ওর বেঁচে থাকার কোন অধিকার নেই,0,crime
ওরে ফাসি দেওয়া উচিচ,0,crime
একে বলে কি হবে মনে চায়ছে তাই করছে। মিলন টা সুখের চেয়ে এখন দুঃখের বাসর ঘর। সালা আইন টা আজ দেশে নাই রে,0,crime
আমাদের বাসায় ভাড়াটে একজন ডিসি অফিসার থাকত উনার নজর খুব বিশ্রী নজর। আমি ভাবি ওরা শিক্ষিত হয়ে এ ধরনের কাজ করে আর অশিক্ষিত মূর্খরা কি করতে না পারে।এই কথাটাও ঠিক যে অনেকে ফাঁদে পড়ে যায় আর অনেকে নিজ থেকেই বেয়াদব। আমার মনে হয় উনি ফাঁদে পড়ে গেছে। কারণ অনেক সৎ ব্যক্তি দেখলাম নিজেদের ইচ্ছে থাকা সত্বেও শয়তানের কারণে নিজেরা ফাঁদে পড়ে যায়।,0,crime
ভিডিওটা দেখে মনে হচ্ছে মিন্নি নিজেই তার স্বামী রিফাতকে খুনিদের হাতে তুলে দিয়েছে তাইতো খুনিরা যখন রিফাতকে টেনে হিঁচড়ে নিয়ে যাচ্ছে তখন মিন্নি খুব স্বাভাবিকভাবেই খুনিদের সাথে হেঁটে যাচ্ছে!,0,crime
সামনের মাসে আসছে বিভাগীয় কমিশনার ফাইল,0,crime
মুন্নি কে আইনের আওতায় নিয়ে আসা হোক এবং সুস্থ স্বপক্ষে বিচার করা হোক,0,crime
তুই কি ওদের ব্যাপারে জানোস নাকি,0,crime
কিস দিলেই জ্ঞান ফিরা পাইতো,0,crime
কি সব ছারে মানুষ,0,crime
ভাই আপনাদের মায়া লাগতে পারে কিন্তু আমার না একে যদি প্রকাশ্যে ফাঁসি দেওয়া হতো তাহলে ভালো হতো বেশি,0,crime
নুসরাত জাহান কে মারার আগে এগুলা চিন্তা করার উচিত ছিল এদের জন্য কান্নাকাটি করাটাও হারাম,0,crime
সৎ পথে করিও ভ্রমন যদিও হয় দেরি অসৎ নারী করিওনা বিয়ে যদিও হয় পরী,0,crime
সিসি কেমেরার ফুটেজ অসসিকার করে,0,crime
আমাদের প্রিয় নবী বিশ্বনবী হযরত মুহাম্মদ সা বছরে তিনি একটা মিথ্যা কথা বলেননি।,0,crime
রিফাতের বাবা মা কি বাভে দেখচে এই ভিডিও টা তাদের কেমন লাগছে,0,crime
সব কথা বাদ রিফাতের হত্যা কারির বিচার হউক,0,crime
অফিসে যেরকম,0,crime
তারে বরকাস্ত করার দরকার,0,crime
এই রকম অসুস্থ মস্তিষ্কের মানুষ ডিসি হয় কেমন করে,0,crime
মিন্নি এখানে প্রত্যক্ষভাবে জড়িত। তারও বিচার হওয়া দরকার।,0,crime
হা হা এইটা বিএনপির কাজ,0,crime
ভাই আমি এক জন 🇮🇳🇮🇳🚨 🇮🇳🌹🌹🌹🌹🇮🇳🇮🇳🇮🇳🇮🇳🍒🍒🍒🍒ভারতের আসাম লখিম পুর আমার বাড়ি আপনারার কাহিনী খুব ভাল লাগছে আমিন দুসীর বিচার চাই,0,crime
ঘরে চিকেন বিরিয়ানি রেখে ফুতপাতের চটপটি খেতে গিয়ে উনার পেট খারাপ হয়ে গেছে বেচারা,0,crime
কেউ কোন বাল ছিড়তে পারবে না। সে সরকারের মাল।,0,crime
ডিসি সাহেব ত আর জোর করে কিছু করে নি সেচ্ছায় দুজনের ইচ্ছায় হইছে।পারসোনাল ব্যাপার।,0,crime
মিন্নি শরীফ কে তার স্বামী হত্যার সাথে জড়িত থাকার কারণে দ্রুত গ্রেফতার করা হোক,0,crime
ঘটনা সত্য ওনার ফেস দেখেই বুঝা যাচ্ছে।,0,crime
রিফাতের স্ত্রী এই ঘটনায় যরিতো,0,crime
ছারের কোন দোস নাই। মজা ছার ও পাইছে আমিও পাইছি।😄😄😋😋🤣🤣😆😆😅😅,0,crime
দেশে বিচার নেই দুই এক দিন এদিক ওদিক করে আবার আগের মত শাসন বা বস্তা চলবে কারন নয়ন বন্ড বাহিনী আওয়ামী ভাবা পনন,0,crime
ওর মাথা থেকে টুপি সরনোহক,0,crime
সালা লুচ্ছামি করে দেখেন সাহেব বাবুর মত কথা বলে কি বলবো ভাষ নাই,0,crime
এই ভিডিও জে দিয়েছে তাকে হাজার কোটি সালাম তার কারনে সত্যি টা আমাদের সামনে এখন আইন অনুযায়ী পুলিশ মেয়ে টিকে গেরেপতার করুক এবং সঠিক সাজা দেয়া হোক।,0,crime
এখানে তো তার স্ত্রী সাভাবিক ভাবে হেটে যাচ্ছে আর রিফাত ভাইকে ধরে নিয়ে যাচ্ছে খুনি রা তার স্ত্রী জরিত আছে এখানে স্পষ্ট বুঝা যাচ্ছে,0,crime
জামালপুরের ডিসি উনার অফিসকক্ষে উনার সহকর্মীরে লাগাইছেন। এই ভিডিওর কল্যানে আমরা জানতে পারলাম ডিসিদের অফিসে খাট পালংক থাকে সেখানে উনারা ইচ্ছামতো গড়াগড়ি দেন ঘুমান একা নিশ্চয়ই শোন তবে অনেকের সাথেই শোন কিনা সেটা বুঝা যায়নি। দৃশ্যত দুইজন স্বেচ্ছায় এই কাজ করছেন। দুইজন প্রাপ্তবয়স্ক মানুষ স্বেচ্ছায় যৌন সম্পর্ক স্থাপন করলে কারোই কিছু বলার থাকেনা। অন্তত আমার কিছু বলার নাই। এখানে ডিসির অপরাধ যে তাকে এই পাবলিক অফিস তার প্রেমিকাকে লাগানোর জন্য দেয়া হয় নাই। তিনি এই পাবলিক অফিস নিজের একান্ত ব্যক্তিগত কাজে ব্যবহার করছেন। ডিসি তার সহকর্মীর সম্মতিতেই তারে লাগাইছেন। কিন্তু এই অফিসে কি তিনি তার চাইতেও বড় অপরাধ করেন না তিনি কি তার এই অফিসে বসেই আমার আপনার অসম্মতিতে আমাদের নাগরিক আর মানবিক অধিকারের শোগা মেরে রক্তাক্ত করেন না করেন। এই অফিসে বসেই তিনি আওয়ামী লীগের হয়ে প্রহসনের ভোট করেন নাই করছেন। পাবলিক মানি নয় ছয় করেননা করেন। রাষ্ট্রের কর্মচারী হয়ে রাষ্ট্র নামের প্রতিষ্ঠানটাকেই ধ্বংস করেননা করেন।তো এই অফিসে নারী সহকর্মীরে লাগাইলে বিচলিত হওয়ার কী আছে বরং বলেন এই ডিসি এতোই ভীরু কাপুরুষ যে যেই নারীর সাথে সে সম্পর্ক করছে সেইটা ভিডিওতে দেখার পরেও অস্বীকার করছে। এইটা ইন্টারেস্টিং আগের রাতে ব্যালট বাক্স ভরা ভিডিও ও যখন বিবিসির ক্যামেরায় ধরা পড়েছিলো তখন এরাই একইভাবে বলেছিলো ওই একটা সেন্টারেই এমন ঘটনা ঘটেছে। ডিসি যদি সত্যিই প্রেমিক পুরুষ হতো তাহলে তার বলা উচিত ছিলো এই নারীকে আমি ভালোবাসি কিন্তু অফিসে আমার এই কাজ করা উচিত হয় নাই। তাই এই কাজটা প্রেম না হয়ে লাম্পট্যতে পর্যবসিত হয়। আমি এই ঘটনা নিয়ে লিখতাম না। কিন্তু আমি বিচলিত অন্য কারণে। আপনারা অনেকেই এই ডিসির সুন্দরী স্ত্রীর ছবি দিয়ে প্রশ্ন করছেন এতো সুন্দরী স্ত্রী থাকতেও কেন ডিসি এই মেয়েরে লাগাইলো এইটা সুন্দর বা অসুন্দরের বিষয় নয়। প্রিন্সেস ডায়না যেকোন বিচারেই ক্যামিলার চাইতে হাজারগুনে সুন্দরী ছিলো তাও প্রিন্স চার্লস কেন ক্যামিলাকেই বেছে নিয়েছিলো এই ঘটনায় নিঃসন্দেহে সবচেয়ে বেশী আহত হয়েছেন ডিসির স্ত্রী। এবং তিনি কোন অপরাধ করেননি। আপনারা কেন তাকে পাবলিক সিমপ্যাথির বিষয় করে তুলছেন তিনি কি আপনাদের সিম্প্যাথি চেয়েছেন মনে রাখবেন এটা নারী পুরুষের অনৈতিক সম্পর্কের বিষয় নয়। এটা বাংলাদেশের গলিত আমলাতন্ত্রের দুর্গন্ধ। এই আমলাতন্ত্রকে সমুলে উৎখাত না করলে আমার আপনার অসম্মতিতেই এই জনপ্রশাসন আমাদের রাষ্ট্র আর নাগরিক অধিকারকে লাগাইতে থাকবে যতদিন না এই রাষ্ট্রটা একেবারে হুড়মুড় করে ভেঙ্গে পড়ে।,0,crime
ভাই সে তো মেয়েরে জোর করে কিছু করে নাই।।মোহাব্বত।। একালে সেকালে বড়কর্তারা একটু আধটু করেই থাকে।।,0,crime
মেয়েটা যে জরিত এতেকুন সন্দেহ নাই,0,crime
রিফাতের বউ কে গেপতার করলেই সব বের হয়ে যাবে কিন্তু মিন্নিকে পুলিশ দরছেনা কেন এটাইত বুজি না?,0,crime
বাংলাদেশ শেষ্ঠ খারাব পুলিশ,0,crime
যতই কান্না কাটি করুক কোনো ছাড় হবে না।। অপরাধ করলে তার শাস্তি পেতে হবেই।। দ্রুত ফাসি দেওয়া হক আসামীদের।।।। আর একটা আমার মেসেজ সবার জন্যে আপনেরা আপনাদের ছেলে মেয়েদের খুজ খবর রাখুন তারা কি করছে।। কোনো খারাপ কাজে লিপ্ত হয়ছে কিনা।।। সব ধরনের খারাপ কাজ থেকে নিজে ও অন্যকে সুরক্ষা রাখুন।।। ধন্যবাদ সবাইকে,0,crime
এটা কি আইন বলে মারধর শেষে এসে দেখি দেখি বলে মানি কি,0,crime
এই ভিডিও দেখার আগ পর্যন্ত ঘটনা অন্যরকম ছিল বাট দেখার পর ওএমজি একটা মের সামনে তার স্বামী মারতে মারতে নিয়ে যাচ্ছে আর সেই মে়েটিই হেলে দুলে যাচ্ছে।। লাইক সিরিয়াসলি???🙄🙄 আচ্ছা এইটা বাদ দিলাম।।। তারপর কোপানোর পর সে কোনো গাড়ি ডাকাডাকি করলো না হাসপাতালে নেওয়ার জন্যে😡😡😡 এই মের ভিতরই গন্ডগোল আছে,0,crime
অবৈধ সরকার অবৈধ কাজকর্ম,0,crime
হাসি লাগে বাংলাদেশের মুক্তি যোদ্ধা অফিস নাকি মদের বার। আর আপু নাকি যানে না জুয়া খারাব কাজ। ভাই পরে গেছে মাংকি চিপায়।,0,crime
হায়রে মানুষ আজ আমার এক ভাইকে কপাচ্ছে আর সবাই চেয়েচেয়ে তামাশা দেখছে। আমরা কত নিচে নেমে গেছি। সবাই যদি এক হয়ে নয়নদের প্রতিহত করত তাহলে আমার ভাইকে লাশ হতে হত না।,0,crime
হে আল্লাহ্ তুমি সবাই রহমত নাজিল😭😭 করো যেনো আর এমন ঘটনা না ঘটে কি বলবো ভাষা হারিয়ে ফেলেছি 😭 একজনের জন্য দুইজন চলে গেলো 😭 এই পৃথিবীতে ছেড়ে যে অপরাধী সে এখন ও বেচে আছে😭 কষ্ট যনম সবাই ভালো থাকবেন খারাপ কাছ থেকে দুরে থাকবেন 😭,0,crime
তাহলে কেন এখন পুলিশ মিন্নিকে দরল ।,0,crime
কি করবেন ভাই এগুলো তো আমি লীগের কুকুর,0,crime
বাবার বিচার ফাসি আর এদের মত লোক নিজের বাহিনি দেশে দোসিদের বিচার নাই অদের মত অফরাদি ফাসি হলো হয়তো আর বাকি লোক ভয় পেতো টা লোক বাচতে গিয়ে এক টি মরেগেলে ও ভাল এই অরা জে মারলো মনে হয় দেশ টা অদের আতে মনে কুনু ভয় নাই,0,crime
এই হত্যা কান্ডের ভিডিওতে দেখে যা বুঝা গেলো তাতে স্পষ্ট মিন্নি ও এই হত্যা কান্ডে অভিযুক্ত।,0,crime
এই মেয়ের ফাশি চাই,0,crime
পুলিশের কাজ অপরাধ দমন করা আর এখানে কি হচ্ছে পুলিশ নিজেই অপরাধী। অসকার দাও কাক্কু কে,0,crime
এই রকম বেয়াদব মেয়ে আকাম করছে আবার বলে সারের কোনো দোষ নেই,0,crime
প্রকাশ্যে দুজনকে শাস্তি প্রদান করা হউক তদন্তের নাম করে ফাইলে ধুলো জমা পড়ে যাবে,0,crime
ভিডিও ফুটেজে যা দেখা হল তা থেকে বোঝা জায় মুন্নি নং আসামী।ধন্যবাদ,0,crime
ওরা মিন্নির উপর হামলা করেনি দুষ তো মিন্নি করেছে আমি নিশ্চিত মিন্নি তাদের সাথে জড়িত,0,crime
সৌদি আরবের মত আইন না কোরআন এর আইন দিয়ে দেশ চললে এ জাতীয় ঘটনা ঘটার সুযোগ থাকে না কারণ সেখানে নয়ন দের জন্ম হওয়ার কোন সুযোগ নেই সৌদি আরব ও কোরআন এর আইন আংশিক আছে,0,crime
এখানে যতো কাপুরুষ দাঁড়িয়ে তামাশা দেখছে সবাই কে লাখ করে জরিমানা করা উচিত।,0,crime
ভাই ক্যামেরা কে লাগাইছে এটাতো দেখার বিসয়না ডিসি অপরাধ করেছে এটাই সত্য আর বাস্তব ওকে আপনি পাগলের মত ছয় কে নয় বানানোর চেস্টা করে জ্ঞানহীনতার পরিচয় দিয়েননা ওকে,0,crime
আমরা কী পারি না সবাই মিলে প্রতিবাদ করতে পারি না আমাদের সবাই সবার মতো করে বাঁচতে আর কতোদিন এভাবে কাটাবো আমরা আমাদের সরকার ভালো চাই যে দুই জন আছে তাদের বাদ দিয়ে নতুন সরকার চাই,0,crime
আপনি এত সুন্দর কথা বলেন,0,crime
আমরা বাংলাদেশের মানুষ অনেক খুশি ফাঁসি চাই আমরা সবাই,0,crime
ফাঁসি এখনো হয়নি তো। অপেক্ষায় আছি,0,crime
সাজানো না ওই অপরাধী,0,crime
পুলিশ হল আসল মদদদাতা ✋,0,crime
নুসরাতের আত্মা শান্তি পাবে । ওদের তাড়াতাড়ি ফাঁসি চাই ।,0,crime
পূর্ব পরিকল্পিত হত্যাকাণ্ড,0,crime
আমি সৌদি প্রাবাসি আমার একটা জারি বানান লাগবে পরবেনএটা আমার ইমু নামবার পারবোন,0,crime
ওএসডি করেই শুধু এর শাস্তি শেষ কি ওই ডিসিকে বরখাস্ত করা হোক।,0,crime
ভাই এতে কিছুই হবেনা শুধু শুধু সময়ে নষ্ট,0,crime
আমাদের দেশের ডিসি এসপি মন্ত্রীরা দেশের গুহা মারছেই পাশাপাশি সহকারী এম এল এস এস কে ছাড় দিতে বাদ্যনয়। সাবাস ডিসি সাহেব চালিয়ে যান আর না পারলে টেবলেট খান। যেমন সরকার তেমন প্রসাশন🤔😇 চেতনার আদান প্রদান করতেই হবে থু 🖕👎,0,crime
সাবাস বাংলাদেশ এগিয়ে যাও,0,crime
অপরাধীদের ফাঁশি চাই।,0,crime
আপচচ হয় রক্ত মাথায় উঠে জায় মাননীয় প্রথান মন্তীকে আমার বলবো সবাই রিফাত হত্যার সবার জেন ফাঁশি হয় তা হলে অনতত সবাই সর্তক হবে,0,crime
একটা ফালতু মেয়ের খপ্পরে পড়ে ব্যাচারার ক্যারিয়ার শেষ।,0,crime
যেমন কর্ম তেমন ফল উচিৎ শাস্তি খুব প্রয়োজন বিনা দোষে একজন মায়ের কোল খালি হয়েছে তোরা তো দোষ করেছিস তোদের শাস্তি হতেই হবে।,0,crime
এইসব ফালতু ভিডিও করে ছেলেপেলে আরো নষ্ট হয়ে যাই যত্তোসব এদের খেয়ে দেয়। কাম নাই নাকি,0,crime
মিন্নির স্বামিকে কয়েকজন মিলে জোর করে ধরে নিয়ে যাচ্ছে মারতে মারতে টেনে হিছরে নিয়ে যাচ্ছে। কিন্তু মিন্নী ধিরে ধিরে হেটে যাচ্ছে মনে হচ্ছে তার কোন সমস্যাই নাই এটা দেখে একটা বাচ্চা ও বলবে যে এই ঘটনার সাথে মিন্নী জরিতো,0,crime
ছি ছি হাইরে বাংলার মানুষ। তোদের কে ধিক্কার জানাই। একটা ছেলে কে কুপাইতাছে আর সবাই দারাইয়া দেখতাছে। কতোটা অসোহাই আমরা।,0,crime
রুমি খাতুন কারেট বলছেন,0,crime
জেলা প্রশাসকের দুই গালে জুতা মারো তালে তালে !!,0,crime
তদন্তের কি দরকার সব কিছুই তো স্পষ্ট।,0,crime
সব আসামীর ফাঁসি মানলাম কিনতু আরেক জন কৈই নং আসামী পুলিশ আফিসার মোজেম কৈই,0,crime
মিনিটে আজকাল কিচুই হয় না মাননিয় স্পিকার ! রহস্যের গন্ধ পাচ্চি,0,crime
কৃষ্ণ করলে লীলা খেলা আমরা করলে কেলা কেলা। ভিডিওটি মিনিটের ভিডিওটি মিনিটের।,0,crime
এই ছেলেটার নামে যদি এতোগুলো মামলা থাকে তাহলে পুলিশ কেন আগে গ্রেপতার করে নি।। দেশে কিসের আইন চলছে সেটাইতো বুঝি না।।,0,crime
বৈরাগী চ্যানেলে আরো ভাল কিছু চাচ্ছি। আশা করি পাবো ।,0,crime
এই হল সোনার সোনার সোনার বাংলাদেশ,0,crime
এই কমেন্ট৷ গুলি ডিসির চুখে পরবে নাকি।ছি ছি ছি।লজ্জা লাগে। উনাদের মত ভদ্র লুকেরা কিভাবে বউ বাচ্চার সামনে মুখ দেখায়,0,crime
মেয়েরা এত খারাপ এসব মেয়েদের কাছ থেকে সহজ সরল ছেলেদের অনুরোধ করছি। তুমরা ধুরে থাকো। এরা সব কিছুই করতে পারে টাকার জন্য,0,crime
ভাই চার মিনিট না পুরো মিনিট আমি এইমাত্র একটা আইডি তে দেখলাম,0,crime
আমরা নিরীহ মানুষ অপরাধ করলে অপরাধী পুলিশ অপরাধ করলে অপরাধ না,0,crime
এখানে অবশ্যই মুন্নি জড়িত সন্ত্রাসীরা ওকে এভাবে কিছু একটা করবে তাহলে ওর স্বামীকে কেন কলেজে নিয়ে গেছে? চেহারার মাঝে কোন পরিবর্তন নাই নয়ন মারা যাওয়ার পর মুন্নির মন খারাপ হয়ে গেছে ও খুশি হয় নাই,0,crime
মিন্নি অপরাধী কিন্তু এর থেকে আরো বড় অপরাধী রয়ে গেছে।এই ঘটনায় মিন্নি অপরাধী তবে এমন অপরাধী না যে রিফাতকে দুনিয়া থেকে সরিয়ে দিবে।এখানে প্রভাবশালীরা গেইমস খেলছে।আর গেমের বল মিন্নি।,0,crime
ভাই বাংলাদেশে ব্যভিচার এর আইন আছে। আপনি হয়তো জানেন না। ব্যভিচারের আইনে তাকে গ্রেফতার করা যায়।,0,crime
একদম সিউর মিন্নি এই হত্যা কান্ডে জরিত এর বিচার চাই এসব মিন্নির জন্য হাজারো ছেলেরা মারা জাচ্ছে,0,crime
আমার মনে হয়না টি মেয়ে যেনে শুনে নয়নের মত সন্ত্রাসীর কাছে যাওয়ার জন্য নিজের স্বামীকে খুন করবে!! আর এটা পাগলেও জানে জনকে মেরে আরেক জনকে বিয়ে করা সম্বব নয় কারন সেও ফেসে যাবে আর মেয়েটা চাইলে তো নয়নকে বিষ দিয়েই মেরে ফেলতে পারতো অথবা ডিভস দিয়ে আবার নয়নের কাচে ফিরে যেতে পারতো।।। এখানে যারা নিন্নির দোষ দিচ্ছে তাদের মাথায় সমস্য আছে।,0,crime
ইসলামি আইননে বিচার করলে এসব বেহায়াপনা করার কেউ সাহস পাবেনা,0,crime
পুলিশ কি করে গুস খেয়ে ছেড়ে দেয়,0,crime
তোর জামাই এখনো তোকে ছারে নায়,0,crime
বাড়ির লোকেরা নাটক করছে,0,crime
যে ভিডিওটা করেছে তাকে ফুলের মালা দিয়া দরকার,0,crime
ভাই এগুলো আর কি দেখব এগুলো সব সময় থাকবে ই যাক পৃথিবীর জানা অজানা অনেক রহস্য নিয়ে সুন্দর সুন্দর ভিডিও আছে আমার চ্যানেলে ।একটু কষ্ট করে ঘুরে আসতে পারেন আমার চ্যানেল থেকে আশা করি আপনার পছন্দের সব ভিডিও দেখতে পারবেন,0,crime
সংসার থাকার পরো মানুষ এমন জঘন্য কাজ কি ভাবে করে। এমন পুরুষ মহিলার জন্যে আজ কোন সমাজ সভ্য সমাজ হতে পারে নাই।,0,crime
পরিবেশ টা সুন্দর না কই কোনো হৈ চৈ আছে,0,crime
সিসি ক্যামেরা তুই অপরাধী রে! কর্মক্ষেত্রে এমন হাজারো অবৈধ গোপন অভিসার প্রতিদিন ঘটছে। ডিসি সাহেবের ভাগ্য খারাপ যে তারটা সিসি ক্যামেরায় ধরা পড়েছে।,0,crime
তে ফ্রি খাবার দেয় ।অবাক কাণ্ড ।অদ্ভুত এ দেশ ।,0,crime
পরিবারের সদস্যদের কি দোষ তারা তো হয়ত অনেকেই জানত না তাদের সন্তান এমন একটা কাজে জড়িয়ে যাচ্ছে।।।। আপনাদের কে আল্লাহ ধৈর্য ধরার তৌফিক দান করুক।।।। আর এই জানোয়ার গুলোর ফাসির রায় দ্রুত কার্যকর করা হোক।,0,crime
বালের প্রশাসন । অনিয়ম ই নিয়ম,0,crime
আরো কত কী যে দেখব সামনে আল্লাই জানে,0,crime
দেশ টা আগে ছিলো দরিদ্র সীমার নিচে এখন চরিত্র সীমার নিচে,0,crime
সকাল টায় কলেজ গেলে। কলেজ দিয়েতো রিফাতের চলে আসার কথা।আর মিন্নি ক্লাসে যাবার কথা।সে কেনো রিফাতকে আটকে রাখলো তারা বাড়ি ফিরতে চাইলে কেনো।সন্দেহকারী সকলকে আইনের আওতায় এনে রিমান্ড দিয়া হোক,0,crime
সারের কোন দুষ নাই তাইলে দুষটা কার যারা ভিডিও ভাইরাল করছে তাদের,0,crime
পরকিয়ায় ছেয়ে গেছে দেশ। আল্লাহ সবাইকে হেদায়েত দান করুন।,0,crime
আহারে লাইলি মজনুর মিলনটা আর দেখলাম না☺,0,crime
আরে বাহ এটা তো দেখছি জেওতা সিনেমা 🤣🤣🤣,0,crime
যে ভিডিও টা করেছে তাকে নবেল দেওয়া হোক 🙃 তার জন্য জাতি আজ ডিসির বিশ্রামাগার কেন দেওয়া হয় তার আসল কারণ জানতে পারলো।,0,crime
ইউটিউবে হা হা রিয়েক্ট দাবি করছি 😂😂,0,crime
আরে ভাই ফাঁসি টা একটু দেখান ভাই কখন ফাঁসি হবে?,0,crime
নুসরাতকে এর থেকে কয়েকগুণ শারিরীক আর মানসিক কষ্ট দিয়ে হত্যা করা হয়েছে😢,0,crime
এগুলো দেখতে খুব ভালো লাগতেছে,0,crime
খুনের সাথে মিন্নি জড়িত। কারনে সে যদি জড়িত না থাকতো শুরু থেকে তার স্বামিকে বাঁচানের চেষ্টা করতো আশে পাশের মানুষের কাছে কান্না করে সাহায্য চাইতো। যা স্বাভাবিক ভাবে স্বামিকে বাঁচানোরর জন্য সব মেয়েরা এটা করতো কিন্তু মিন্নি জড়িত বিধায় এটা করেনি ।,0,crime
সুমন ভাই সাজা যেনো পাই,0,crime
হাছিনা আপকে আর কাদের মামা দিয়ে তন্নতো করা হউ,0,crime
আমি একজন সাদারণ জনগণ হলেও আমি মন থেকে ভালোবাসি বাংলাদেশ আওয়ামিলিক কে বাংলাদেশের প্রধান মন্ত্রীর উদ্দেশ্যে কিছু কথা বলতে চাই দেশে যে পরিমান উন্নয়ণ হচ্ছে সেটা সারা বিশ্বে অনেক প্রশংসনিও সেটা থেকে আমরা মনে করতে পারি বাংলাদেশের মেরুদন্ড শক্তিশালী করতে হলে আইন ও বিচার বেবস্তা কে দেশের মানুসের সারতে নিয়াই বিচার নিচ্চিত করা বিশেষ প্রয়োজন এটা আমরা আপনার থেকে আশা করতে পারি কেননা সবকিছু যেরকম আপনার মাদ্দমে সম্বব এটাও আমরা আপনার কাজ থেকে আশা করি আপনি পারবেন,0,crime
রান্না করতে গিয়ে হাতে একটু ছ্যাঁকা লাগলে কেমন লাগে??? আর একটা মেয়েকে পরিকল্পিতভাবে ঠাণ্ডা মাথায় জ্যান্ত পুড়িয়ে মারলো কতটা কস্ট নিয়ে একজন মানুষ মারা গেছে ভাবতেই গা শিউরে উঠে😪😪 বিন্দুমাত্র সহানুভূতি নেই এইসব খুনী এবং তার পরিবারের উপর,0,crime
ভিডিও টা দেখে কেন যেন মনে হলো রিফাত এর স্ত্রীও জরিত আছে।।।।।৷ আমরা চাই রিফাত এর স্ত্রীকেও রিমান্ডে নিয়ে জিজ্ঞাসাবাদ করা হোক।।।।,0,crime
কুকুরের কখনো কাপড় পরতে হয় না,0,crime
মানুসেরকে মারারসমায় মনতাকেনা,0,crime
এই গুলি টাকা জোগার করার পদ প্রতিবাদ করেন রিফাত হ্যাত কে নিয়ে এই গুলি না করে,0,crime
এর একমাত্র শাস্তি ক্রসফায়ার !,0,crime
মানুষ কতটা পাগল হলে নিজের খারাপ কাজের তদন্ত করতে চায়। আপনারা যদি বলেন একটা রোষ্ট করতে চাই। আগুন ছাড়া।,0,crime
ভাই কি নিউজ করেন এই গুলা। এই সবই তারেকজিয়ার ষড়যন্ত্র । এই জাতীয়তাবাদী নেতা আজ এই লীগের ষড়যন্ত্রের শিকার। একদিন ইতিহাস কথা বলিবে। । এগিয়ে চলো লীগের ভাইয়েরা তবে পুলিশ সরে গেলে পালাবার পথ রইবেনা,0,crime
এগুলা এডিট করা যায় ভাই🤣🤣🤣🤣,0,crime
রিপাত যে কলেজে আসবে নয়নরা জানলো কি করে মিন্নি বলেছে তাই সব এসেছে প্রেন করে,0,crime
এখন কেমন লাগে আপনাদের এমনি লেগেছিল নুসরাতের পরিবারের কাছে,0,crime
দারুন ভাই মজা পাইলাম,0,crime
সিনেমার শুটিং দেখলাম মাটিতে গোসল কর তারপর ও তোদের এই কান্নার মূল নেই অাহারে কি যানি কত কষ্ট না পেয়েছে নুসরাত,0,crime
বাঙালী তো লাঙ্গল চালাবেই। মাঠে না হলে খাটে। লাঙ্গল চলবেই,0,crime
ভাই লিং হবে নাকি,0,crime
এই করার কি খুব দরকার ছিল আমাদের প্রতিবাদ করা উচিং,0,crime
সাংবাদিক মাসুদা ভাটটি কোথায় এখন। এটা মঈনুল সাহেব হলে মিডিয়াতে এখন কি চলতো।,0,crime
সটিক বিচার আশা করি,0,crime
হত্যার সঙ্গে জড়িতদের সবার শাস্তি দেয়া হোক সবাইকে স্পষ্টতই দেখা ও চিন্হিত করা যাচ্ছে।,0,crime
পরি চালেক নাম বার দাও,0,crime
এতো মানুষ থাকার পরেও ছেলেটাকে কিভাবে মারলো,0,crime
এই চ্যানেল খুনিদের সহযোগী চ্যানেল। তা না হলে অপরাধীদের কান্নার খবর কেন প্রচার করছে? তাই এই চ্যানেলের মালিককেও মৃত্যুদন্ড দেয়া উচিত।,0,crime
কোন খমা হবে না।,0,crime
দূত ফাসি চাই জন খুনির,0,crime
এই পোলাটায় কতকিছু জানে রে বাবা,0,crime
আসলে ভাই কি বলবো বলার মত ভাষা হারিয়ে হারিয়ে গেছে একজন স্ত্রী এভাবে স্বামীকে আমার মনে হয় মিনি সব ষড়যন্ত্র মিনি জড়িত আছে এই কাজগুলো,0,crime
আমরা বুঝতে পারছি ছারের মাইরে আপনি সন্তুষ্ট হইছেন সেই জন্য সারের দুষ দিতে চাননা যাতি বুজেছে আপনি আবার সারের কাছে জাইবেন তাতে কিনু সন্দেহ নাই! আর আপনি বিচার চাওয়া অচিত আমি মনে করি এতো চিপায় কোন চিটার কেমেরা লাগাইছে🤣😂🤣😂😂😂,0,crime
তোমার মুখে দারি কই ভাইয়া এত কথা বল নিজের আমল ঠিক নাই কেন,0,crime
সোনার সন্তানদের কিছু হবে না 🙄,0,crime
আদালত সুন্দর একটি রায় দিয়েছে। ওদের তারা তারি ফাঁসি দেওয়া হক।,0,crime
দ্যাখ কেমুন লাগে,0,crime
দুঃখজনক হলেও সত্য তবে এটাতো একদিনে হয়নি তাহলে আইনশৃঙ্খলা বাহিনী ও সংবাদ কর্মী ভাইয়েরা আপনারা এতো দিন কোথায় ছিলেন।,0,crime
ওকে বহিস কার করা হক,0,crime
দোষ থাকতো কেনো মজা তুমিও পাইসো মজা স্যারও পাইসে😥,0,crime
আলহামদুলিল্লাহ। সব খুনিদের যদি এভাবে বিচার হত!!,0,crime
এদের কান্না দেখে অনেক খারাপ লাগার কথা কিন্তু কেন জানি এক পৈশাচিক আনন্দ পাচ্ছি।,0,crime
ভিডিও ফুটেজে যারা যারা জরিত সব খনিদের ধরার জন্য অনুরোধ করছি,0,crime
নুসরাতের পরিবার ও এইভাবে কান্না করেছিল। নুসরাত ও এই ভাবে কষ্টে মারা গিয়েছিল। ও কষ্টের ভিডিও এখন ও এ আছে। যা দেখে আয় কিভাবে ও কষ্ট পাইছে।,0,crime
ভাই আমি পেডিষ্ট উল্লাস শেরপুর থেকে আপনাকে খুব দরকার প্লিজ আমাকে একটা ফোন দিবেন,0,crime
মাতা নিছু করেকে যারা অপরাদ করে সে আমি করিনি তাহলে আমি ভয় পাবকেনো,0,crime
অপরাধী চোখ অঙ্গভঙ্গি দেখেই সব ক্লিয়ার,0,crime
অনেক দিন চেষ্টা করে যে শেম্পু আউট করতে পারিনি আজ ডি সির ডগ স্টাইলের মাইর দেখে বের হয়ে গেলো সান্তি পাইলাম,0,crime
যা বুঝলাম এই ঘটনা ঘটবে মিননী আগে থেকেই জানতেন যখন রিফাত কে ওরা ধরে নিয়ে যাচ্ছিল মিননী খুব সাধারণ একটা মেয়ের মত হেটে যাচ্ছিল মনে হচ্ছিল রিফাত তার কেউ না।,0,crime
দুজনেরই দৃষ্টান্তমূলক শাস্তি চাই,0,crime
তবে সমস্যা এখনো তোদের,0,crime
ডিসি আর ঢালতে পারবে না তাই ভং,0,crime
তুই বেটা কোন্ দেশের পাগল রে ভাই? সালামটাও দিলি না শুদ্ধ করে তারপর এমন স্টাইলের কথা বাংলা না ইংরেজি বলছিস্ বুঝতে কষ্ট হয়েছে ।তাছাড়া কি দোষে ফাঁসি দেওয়া হয়েছে তাও তুমি জানো না? যাও দুদু খাওয়া গিয়ে ।বেচারা!,0,crime
একটু রুমে নিয়ে গিয়ে ঢেলে দিয়েছে😂,0,crime
এইসব কি কেয়ামত এর পূর্ব লক্ষণ নয়,0,crime
ডিসি হয়ছে অনেক কষ্ট করে এখন একটু আনন্দ ফ্রুর্তি করবে সঙ্গে ছোট কর্মচারীদের সংসার একটু ভালভাবে চলার ব্যবস্থা করছিল সেটা আর হলো না আকাম করবি কর ক্যামেরা যেখানে ছিল না সেখানে যাইতি ক্যামনে যে ডিসি হয়লো বুঝলাম না,0,crime
বিস্বাস যোগ্য না,0,crime
এটা অত্যন্ত সুষ্পষ্ট যে ঘটনার নেপথ্যে এই ড্রামাকারী নারী মিন্নি। যেহেতু নয়ন বন্ড ফরাজী ও মিন্নি একই অপরাধে অপরাধী তাই পরিনতি একই হওয়া উচিৎ। এক্ষেত্রে মিন্নির পরিনতি ভয়াবহ হওয়া দরকার। এই জন্য যে সে এই হত্যা কান্ডের মূল হোতা। আজ আমার এ দাবী আপনারা মানেন বা না মানেন তদন্ত শেষে আসল রহস্য বেড়িয়ে আসবেই। এজন্য মিন্নি দ্রুত গ্রেপ্তার করে আইনে আওতায় আনা দরকার। কথায় আছে না,0,crime
এটা বাংলাদেশ এই দেশে সব সম্ভব ।,0,crime
মনে হয় তিনাদের স্বার্থে ঘা লাগছে তাই অবশেষে অভিযান। যাইহোক চুনোপুঁটি নয় রাঘববোয়ালদের সামনে দেখতে চায় জাতি।,0,crime
মিন্নির বিচার চাই,0,crime
শুধু ডি সি কেন মহিলাটাও খারাপ মহিলারা সুবিধা পাওয়ার আশায় অফিসে এসব করে থাকে। যে সব মহিলা চাকরি করে তাদের বেশির ভাগই খারাপ।,0,crime
আল্লাহই আইন করে দিয়েছে খুনের বদলে খুন।,0,crime
বদমাইশ নিজের নাম নিজেই দিসে মনে হছে নয়ন বন্ড,0,crime
সাধনাই ক্যামেরা লাগিয়েছে এটা প্রথম ভিডিও দেখেই বুঝেছি।আমি পুরো একমত আপনার সাথে কিছু মানুষ না বুঝেই গালাগাল করছে ওরা সাধনার চাইতেও খারাপ।,0,crime
রিফাত সরিফ ভাই। মিন্নিকে সঙ্গে নিয়ে যখন কলেজ থেকে বাড়ি যাওয়ার উ‌‌‌‌র দেশে। কলেজ গেটের সামনে রাস্তায় রিফাত সরিফের পেছনে পিছনে ঠিক ঠাক মতো আসছিলো বাইকের কাছে। কিন্তু সেই সময় মিননীর চলার পথে চোখে মুখে ও তার চেহারার একটা আতঙ্কে ভাব দেখা যাচ্ছে। মিননি সামনে দিকে তাকিয়ে তাকিয়ে যখন দেখতে পাই নয়ন শালাদের গ্রুপের হারামী বজ্জাত ছেলে গুলো দাড়িয়ে আছে রিফাত সরিফকে মারার বা হত্যার করার জন্য। তখনই মিননি রিফাত সরিফের পেছন থেকে কেটে আবার ফিরে য়াচছে কলেজের দিকে। তার কারণ এখানেই বুঝতে পারছি যে মিননি রিফাত সরিফের হত্যাকারীদের সাথে জড়িতো আছে। ইচ্ছা থাকলে মীননি রিফাত সরিফ ভাইকে বাচাতে পারতো। মিননির সামী রিফাত সরিফ ও বুঝতে পেরেছেন যে মিননি ও জড়িত আছে হত্যাকান্ডের সাথে। সেই জন্য রিফাত সরিফ ভাই মীননি উপর রাগ অভিমান করে চলে গেছে একা একা সাথে মিননি কে না নিয়ে। দোয়া করি আল্লাহ যেনো রিফাত সরিফ ভাইকে জান্নাত বাসী করিও।আপনারাও আল্লাহর নিকট দোয়া করবেন রিফাত সরিফ ভাইয়ের জন্য। আল্লা হুমা আমিন।,0,crime
আমি ভিডিওটা লক্ষ্য করে দেখলাম মহিলাটা বারে বারে ওই প্রশাসকের গায়ের উপরে গিয়েছে। অতএব তার বিরুদ্ধে কোনো ব্যবস্থা নেওয়া হইতেছে না শুধু পুরুষদের বিরুদ্ধে ব্যবস্থা নেওয়া হবে আল্লাহপাক রাব্বুল আলামীন পবিত্র কুরআনুল কারীমের মধ্যে বলে দিয়েছেন যেনাকারীর কথা পরে যেনাকারী নি কথা আগে।,0,crime
মিন্নি কিন্তু সেই,0,crime
সাংবাদিক কথা বলতে ভয় পাচ্ছে,0,crime
আরে যেরা আইনের কাজ করে তারাইতো বেইন করে।,0,crime
কেমরা কি করলো এরে হালা তোর কোনো কাম নাই,0,crime
এটা কি স্বাধীনতা।স্বধীন দেশ।এক জনের বিপদ দেখে অন্য জন পালায়।সবাই এগিয়ে আসলে দু চার জন কিছু করতে পারত না।মেয়েটি ছাড়াতো কেউ এগিয়ে আসেনি ।তদন্ত না করে কাওকে দোষ দেয়া ঠিক না।কে মূর্খ কমেন্টস পরলেই বোঝা যায় ।,0,crime
এটা কোনো ঘটোনা এটা বাংলাদেশের সাধারণ ঘটোনা এটাই প্রাধান কাজ । সরকারী লোকের কোনো বিচার হয় না ।এটা বাংলাদেশের মানুষ কি জানে না ।,0,crime
দুর্জন বিদ্বান হলেও পরিত্যাজ্য।,0,crime
একটা মানুষকে পুড়িয়ে মারা সময় একবারও মনে পড়ে নাই তার ফ্যামিলির অবস্থা কি হবে এখন দেখ তোর ফ্যামিলির অবস্থা কিরম হচ্ছে আর কেমন লাগছে আমি দেশের জনগণের সাথে তাদের ফাঁসি দেখতে চাই এবং আর কেউ সাহস না পায় এইরকম কাজ করার জন্য,0,crime
আওয়ামীলীগ নেতার বাড়িতে আছে খুনি,0,crime
প্রথম বিয়ে গোপন করে দ্বিতীয় বিয়ে রিফাত স্ত্রীর ? ?,0,crime
মিন্নিকে পুলিশ কেনো এরেস্ট করেনা ? বুঝলামনা ওকে কে সেভ করছে আবার ওকে নাকি পুলিশ পাহারায় রেখেছে তাহলে ওকি উপরমহলের খাবার ? যদি তাই হয় তাহলে আপনারা নিচ্ছিত যে বিচার কখনোই হবেনা,0,crime
সত্যি এটায় বাস্তব,0,crime
ছেলেটা কে মারার পিছনে এ মেয়েটার হাত ছিল কেননা যে ছেলেটা এই ছেলেটা কে মারছে তার সাথে অনেকগুলো ভিডিও সোশ্যাল মিডিয়াতে এসে গেছে ওর অনেক গুলো ফটো ভিশন মিডিয়াতে এসেছে আর একটাতে এমন ভাবে দেখা গেছে যে সেই ছেলেগুলাকে কেক খাইয়ে দিচ্ছে এবং ছেলেরা ওকে কেক খাইয়ে দিচ্ছে এবং কি তার হাজবেন্ডের সাথে একটা ফটো দেখা গেছে যে পোশাক গায়ে দেওয়া ও সেম টু সেম পোশাক দেওয়া ওই ছেলেটা যে ছেলেটা ওই ছেলেটার সাথে একটা সেলফি দেখা গেছে তার মানে মেয়েটার বিয়ে হওয়ার পরেও ছেলেটার সাথে অবৈধ সম্পর্ক ছিল তাই তারা ষড়যন্ত্র করে তার হাজবেন্ডকে মারার পরিকল্পনা করছে কেন নাম মেয়েটা প্রথম বলছে যে ও ছেলেটা তাকে ছেড়ে সানি খুতবা ওর সাথে কোন রিলেশন নাই বা বিয়ে হয় নাই তো বিয়ে যদি না হয় তাহলে এখানে কাছে নিজে একটা অফার অফার অফার টা কোথায় থেকে আসে এক দ্বিতীয় নাম্বার হচ্ছে তোমার যদি ওর সাথে যদি কোন রিলেশন নাই থাকে তাহলে এখানে ফাটা কিভাবে আসলো যে কে খাইয়ে দিচ্ছে এবং কি তোমাকে খাইয়ে দিচ্ছে দ্বিতীয় কথা হচ্ছে মেয়েটা সেম টু সেম পোশাক গায়ে দেওয়া তার হাজবেন্ডের সাথে আছে এবং ওই ছেলেটার সাথে সেলফি তদন্ত করে আইনের আওতায় আনা উচিত কেননা গ্রুপটা যে মেয়েটা হেল্প করছে কেন না যতক্ষণ পর্যন্ত নিজের ঘরের একটা সদস্যের সাথে মিলিত না থাকে ততক্ষণ পর্যন্ত সুর কখনো আরেকজনের ঘরে এসে চুরি করতে পারে না কেননা নিজের ঘরের মানুষ শামিল থাকলে তখন সঠিক কাজটা করতে তখন হিম্মত করে এবং কি ও আসানিসে সহজ ভাবে চুরি করতে পারে আমি যেটা বুঝতে পারলাম এই কাজে ব্যবহার মেয়েটার ঠিক আছে ভালো করে তদন্ত করে দেখেন আপনারা এই মেয়েটার এখানে হান্ডেট পার্সেন্ট সিওর মেয়েটার দোষ আছে,0,crime
কেউ আমাদের লিঙ্ক দে আমি আগে দেইখা লই,0,crime
কেডাকাদেবলছে।একরাতেদরাসম্বনয় জদীকেডাকাদেরকেমাত।বিশমিনিটেরদরেপেত।,0,crime
ডিছিকে এবার দাও কেছি,0,crime
আগে জানতাম হ্যাকাররা আইডি বা তথ্য হ্যাক করে পাবলিশ করে কিন্তু হ্যাকাররা ভিডিওতে পেন্ট খুলে ফেলতে পারে এই কথা বাপের জন্মেও শুনিনাই😂😂😂,0,crime
যাদের মধ্যে জবাবদিহিতা দ্বীনদারী এবং আল্লাহর ভয় নাই তাদের দ্বারা সব অপকর্মই সম্ভব,0,crime
মা বাবা কে বলছি সন্তান দের সু শিক্ষা দিয়ে তুলুন । তাহলে এভাবে গাড়ির পিছনে কাঁদতে হবে না । আল্লাহ কে বিচার দিয়ে লাভ নেই। কারন আল্লাহ সব জানেন । ।। ।,0,crime
কেউ দৌড়ে পালায় নিজের আত্মসম্ভ্রম আত্মসম্মান কিংবা আত্মমর্যাদা রক্ষা করতে আবার কেউ পিছনে দৌড়ে বেড়ায় তার আত্মসম্ভ্রম আত্মসম্মান কিংবা আত্মমর্যাদা উড়িয়ে দিতে। সামান্য একটা নিউজের জন্য এটা কি খুব জরুরি আমার মতে এটা মোটেও কাম্য নয়। সবার পরিবার আছে তাদেরও আত্মমর্যাদা আছে। আ মরা রাতের আঁধারে কিংবা দিনের আবেষ্ঠিত অন্ধকারে কম বেশি কত না জঘন্য অপরাধ করে থাকি। পার্থক্য শুধু এতটুকুই উনাদের টা বাইরে প্রকাশ পেয়েছে আর আমাদের টা গোপন আছে। উপরওয়ালা ভাল জানেন। আমরা বাঙালী যে কত নিকৃষ্ট ভাষায় কথা বলতে পারি তার জন্য আপনারা নিজেদের কমেন্ট গুলো একবার হলেও ভাল করে পড়ুন আর ভাবুন তো সেই মহিলার ভাই অথবা বাবা পড়তেছেন এবং নিজেকে সেই স্থানে দ্বার করিয়ে দেখতে চেষ্টা করুন প ারবেন উনারা যা হারাবার তা হারিয়েছেন ফিরে আর কোনদিন পাবেন না। যা আছে তা নিয়ে তাদেরকে বাঁচতে দিন। সবার প্রতি আমার একটা অনুরোধ এভাবে নিকৃষ্ট ভাষায় যেখানে সেখানে কমেন্ট করে নিজেদের বংশের এবং মূর্খতার পরিচয় দিবেন না জানি কোথাও কমেন্ট করে কারো কিছু আসে যায় না তারপরও বলি সৃষ্টিকর্তা এক তিনি সব দেখছেন উনার বিচারের আইনও এক ভিন্ন জনের জন্য ভিন্ন হতে পারে না। কারোও সম্বন্ধে যেকোন বিষয়ে কমেন্ট করার আগে শুধু একবার ভাবুন এই ঘটনা টা আমার সাথেও ঘটতে পারত। ভালো থাকবেন ভুল হলে ধরিয়ে দিবেন। এইচ এম জাকির।,0,crime
মিন্নি সে অপরাধী,0,crime
ছেলেটা কে যখন ধরে নিয়ে যায় মিন্নীর হাটা ধির গতিতে ছিল এ দৃশ্যটা আমি অনেক বার টেনে টেনে দেখছি মেয়েটা জরিত ছিল তাকে ও রিমান্ডে নেয়ার দরকার এই ধরনের মেয়ের জন্য আর কোন মায়ের বুক যেন খালি না হয় একটা মেয়ে কয়টা মায়ের বুক খালি করল,0,crime
আল্লাহ আচেই। চাচা ঠিক কইচেন। আল্লাহ আচে জন্যেই এই শুওরের বাচ্চা গুলার ফাসি হচ্ছে।,0,crime
পরিবার জানে পরিবার এহন রাগ হইয়া আরেক জায়গায় চইল্যা গেছে😂😂😂 ?,0,crime
এদের কারনে শেখহাসিনা আজ খমতাইতাই এদের বিচার হবেনা,0,crime
সমস্যা পরে গেছে। যাক যদি নিজের ভুল বোঝতে পেরে ঠিক হয়ে যায়। তাহলে তো ভালই।,0,crime
এ বিডিও টি দেখলে নিজের মনকে শান্তনা দেবার ভাষা থাকেনা। কতটা নিষ্ঠুর মানুষ হতে পারে এত গুলো মানুষ কি করে দাঁড়িয়ে দেখছে রিফাত কে কুপানো অতচয় তারা চাইলে সবাই মিলে একসাথে রিফাত কে বাঁচাতে পারত। তানা করে যে যার মতো বাচার চেষ্টা করল আর জানোয়ারের মতো তাকিয়ে রইল। একটু চেষ্টা করলে আজ অকালে মরতে হতোনা রিফাত কে। অনেক কষ্ট হয় রিফাতের জন্য চোখের পানি চলে আসে নিজের অজান্তে। আল্লাহ যেনো রিফাত কে জান্নাত বাসি করে।,0,crime
রিফাত ফরিং দা দিয়ে সবার আগে কোপ দিয়েছে ভালো করে দেখুন,0,crime
বাহ কি সুন্দর। জেলা প্রশাসকের গোপনীয় শাখার একজন সহকারী ছিলেন তিনি। আমিতো ডিসির চেয়ে সরকারের দোষ বেশি দেখছি। সরকারি অফিসে পুরুষ ডিসির গোপনীয় শাখায় একটা মেয়েকে নিয়োগ দিলে এমন অপকর্ম হবে এটা স্বাভাবিক। এমন ঘটনা হয়তো দেশের আরো গোপনীয় শাখায় হইতেছে,0,crime
যখন নোংরা কাজ করছিলি তখন তোর ছেলের কথা মনে পড়েনি,0,crime
সত্যি স্যরের কোনো দোষ নেই যা করার তো ম্যাডাম করলেন।,0,crime
তুই রাজি হলি কেন,0,crime
রিফাত কে আগে ক্রসফায়ার করা উচিৎ।,0,crime
ওরা ধরা খেয়ে ফেসেছে কত কাহিনী এই রকম সিসিটিভির বাহিরে,0,crime
কখন যেন ওরা বলে যে এটা একটা গুজব !!!,0,crime
মেয়েটা কার সাথে জড়িত আছে বা নাই এগুলা না দেখে আমরা চাই খুনের বিচার এরকম যদি কোন করে যদি কেউ পার পেয়ে যায় অপরাধের সাহস বেড়ে যাবে,0,crime
নারীদের আরো বেশি করে চাকুরী দিন ছেলেদের বেকার করে রাখুন। এই হলে এত হবেই।,0,crime
আপনারা অনেক মানুষে জীবন বাচালেন আপনাদের কি বলে ধন্যবাদ দেবো যারা জুয়া খেলেন তারা এতো টাকা পায় কোথার থেকে এদের কথা শুনে মনে হয় টাকার কোনোই দাম নেই এদের কাছে লাখ লাখ টাকা হেরে কতো সুন্দর ভাবে কথা বলে একটু খোজ খবর নিলে জানা যাবে যারা জুয়া খেলে মাদক সেবন করে তাদের সংসারে কোনো শান্তি নেই এই ক্যাসিনো অনেকের জীবন ধ্বংস করে দিচ্ছে মানুষ অপরাধী হয় এভাবে ওরা যখন জুয়ার টাকা মাদকের টাকা পায় না তখন অপরাধের সাথে জড়িয়ে যায়,0,crime
এদেরকে চাকরি থেকে বহিষ্কার করা হোক,0,crime
বাংলাদেশে মানুষগুলো সচেতন না ।। সব চোর দূনীতি বাজ ঘুষখোর ধর্ষক।।।।,0,crime
আল্লাহ বাংলাদেশে ঠাটা ফেলাও আমিন।,0,crime
আমার মনে হয় মিন্নি জড়িত,0,crime
এইটা মেয়ের দোষ সে যদি ভাল হত এই কাজ হত না খারাপ মেয়ে,0,crime
তোর দরকার আমাকে বলতে আমি লাগাতাম,0,crime
সব নষ্টের মুল মিন্নি আমরা চাই আর সব অপরাধির সাথে মিন্নিকেও শান্তি দেওয়া হোক যাকে বলে প্রোকাশে ফাসি আমরা রিফাত হোত্তার বিচার চাই,0,crime
ভিডিওতে তো দেখাই যাচ্ছে কে কে জড়িত এখানে আর রিমান্ড কি দরকার সোজা তাদেরকে ফাঁসিতে ঝুলিয়ে দেওয়া হোক,0,crime
সাংবাদিক ভাইদের বলছি আপনারা পুলিশের লোক মিথ্যা কথা বলিয়েন না কারন এরা সরকারকে পাইলে এদের নিজের নিজের মনে করে মানুষের জুলুম করে আল্লাহ একজন আছেন খোদার গজব বেশি লাগে না,0,crime
সরম থাকলে কথাও বলতেন না।টিভির সামনে আসা দুরের কথা,0,crime
আমি আসলে আবাক হলাম। এতোদিন হলো আজ ফুটেজ টা বের হলো কারন কি। এতোদিন ফুটেজ টা কুথায় ছিল আর এখন ফুটেজ বের করে লাভ কি। যারা অপরাধী তাদের তো ধরা হয়ে গেছে। এখন বের করে লাভ নেই,0,crime
মিন্নি কে রিমান্ডে নেওয়া হক,0,crime
যেহেতু সে ভুল বা দোষ স্বীকার করেছে এত‌এব‌ তার দিকে ক্ষমারদৃষ্টি দেওয়া উচিৎ।,0,crime
নিজেকে এখন আর বাংলাদেশি ভাবতে ইচ্ছে করেনা,0,crime
একটি মেয়ে অনেক গুলো ছেলের জিবন। নিয়ে নিল। মিন্নির ফাসি চাই,0,crime
যে বাড়িকে পতিতালয় স্বীকৃতি দেয়া হয়েছে সে বাড়িকে পূণ্যের ঘর বলে পরিচিত করার চেষ্টাটা ভালো লাগছে। তবে এ চেষ্টা টিকে থাকবে কি না তা নিয়ে শংসয়ে আছি।,0,crime
প্রধানমন্ত্রী বলার পর অভিযান হলো তাহলে স্বরাষ্টমন্ত্রী ও ক্রীড়া মন্ত্রী কি ঘুমিয়েছিলেন নাকি মন্টু পেতেন,0,crime
এই মেয়ে ডিসির সঙ্গে যতই যৌনকর্ম করুক না কেন সে কিন্তু তার হিজাব এবং পর্দা ঠিকই বজায় রেখেছে হয়তো তার এই হিজাব এবং পর্দার কারণে সে বেহেশতে চলে যাবে তাই বাংলাদেশের আপুরা যত অপকর্ম করুন না কেন হিজাব বা পর্দা বজায় রেখে করবেন,0,crime
চোরের দশ দিন সাধুর একদিন।,0,crime
প্রমান আছে আর কিসের তদন্ত,0,crime
পৃথিবীতে এমন কিছু কান্ড ঘটে যা শুধু বাংলাদেশ বলেই সম্ভব হয় । এই যেমন নিজের অপরাধের তদন্তের দায়িত্ব নিজের হাতেই । যেমন চোরের বিচার চোরের কাছেই দেওয়া ।😬😬😬😬😬😬😬😬😬😮😬😬,0,crime
মেয়েটি সহ ফাসি হোক সৌদিআরব,0,crime
মেয়ে টা অনেক বড় ভূল করেছে তাকে খমা করে দেওয়া হক এবং সে অনেক বড় ভয়ের ভিতরে আছেন,0,crime
মিন্নির ফাসি চাই উচ্চ আদালতে,0,crime
দালালি করতে নামছে। জনের সম্মতিতে করলে পরকিয়া জায়েজ হয়ে যায় তোমরা সমাজের জন্য ভাইরাসের ন্যায়। খারাপ কাজকে ফালতু লজিক দেখিয়ে অনুমোদন দিয়ে দিতেছ। যে এই ভিডিওটা বানিয়েছে তার বোনের হাসবেন্ড যদি এই ডিসির মত কাজ করত তখনও কি তুমি কু যুক্তি দিয়ে কু কাজ কে মহৎ বানিয়ে ফেলতে,0,crime
নিরপরাধ নুসরাত জাহানের জন্য তাঁর মা বাবা নিকট আত্মীয় এর চেয়ে আরো বেশি কেঁদে ছিল আজ অবধি ও তাদের কান্না থামেনি সাথে সারা দেশের মানুষ ও কেঁদেছিলেন মমতাময়ী সত্যবতী ‌ও নিরপরাধ নুসরাত জাহানের জন্য। সত্যিই আপনাদের আপন জনদের পাপের শাস্তির বেদনায় আমরাও ব্যতীত কিন্তু তাঁরা তো যে জঘন্যতম অপরাধ করেছে তার জন্য তাদের শাস্তি অবশ্যই অবশ্যই ভোগ করতে হবে এটাই স্বাভাবিক এবং সারা দেশের মানুষ ও অপেক্ষায় আছে মানুষ রূপি হায়েনাদের অর্পিত শাস্তি কবে নাগাদ দ্রুত কার্যকর করা হয়॥,0,crime
উনি কারো চাপে পড়ে এইসব বলছে,0,crime
এতোজন মানুষ সুধু দেখেই রইলো?,0,crime
চোর এ না শুনে ধর্মের কাহিনী।,0,crime
পুলিশের সাথে কথা বলতে ও ভয় করে তারা তো মানুষ না পুলিশ,0,crime
বিরিয়ানির সাতে শিদল কেলে পেটকারাফত হবেই,0,crime
আসলে ওই আমাদের মতো বিডিও দেইখা যেনো যেই অভিনয় দরকার সেটা বানায়া লাইছে,0,crime
মজার একটা সীমা থাকে।😞😞 বিনা কারনে কেউ কাউরে এমনে মারে না মিন্নি আর বন্ড দলের ফাসি চাই।,0,crime
তদন্ত পর্যন্তই । কঠিন শাস্তি যদি পেতো তাৎক্ষণিক তাহলে বুঝতাম ন্যায় বিচার হয়েছে। সবচেয়ে বেশী ভালো হয় দুজন কে বিয়ে দিয়ে দিলে।,0,crime
রসমালায় ঘরে রখে বাইরে মেয়াদ উওীন ডিম খায় 🥵🥵🤡🤡🤑🤑😱😱,0,crime
মিন্নীর ফাসি চাই,0,crime
এর সাথে মিনি জড়িত আছে,0,crime
মহিলার চেহেরাটা দেখান,0,crime
এটা প্রশাসনের টাকা খাওয়া পলিটিক্স এর আগে কি প্রশাসন বাল কাটছিল,0,crime
এসব কান্নাকাটি করে করে লাভ অাছে। পুরুষ মহিলা সম্মিলিত ভাবে যেখানেই কাজ করতেছে সেখানেই এসব নিরবে চলতেছে। অাজ বাংলাদেশের জন পুরুষ এবং মহিলার চরিত্র প্রশ্নবিদ্ধ।,0,crime
বিডিও থেকে আমি বুসতে পারলামএই নারী সু পরিকল্পিত টাকা কামানোর আসাই এইডিসি ভালভাবে ব্যাবহার করছে নিজে পোসাক খুলছেন এতে কি পমানিত নারী অপরাধী,0,crime
মিনিটের ভিডিও,0,crime
কোটি মানুষ খুশি হয়েছে ।,0,crime
নাইস,0,crime
ছিঃ ছিঃ ছিঃ,0,crime
দেশটা এখন কি অবস্থায় চলছে একবার শুনুন মনের কথা গুলো মিলিয়ে নিন একটু ফ্রেশ হউন,0,crime
চমৎকার বাংলার মানুষ।একটা মানুষকে দুইটা মানুষ কোপাচ্ছে আর পাশে এক গাদা ভীরুর দল।চাপাতি হাতে সন্ত্রাসী সবার সামনে দিয়ে হেটে গেল কিন্তু এখনও তোরা তার স্ত্রীকেই দোষ দিয়ে যাচ্ছিস।নিজেদের দোষ ঢাকতে আরেকজনকে দোষী বানানো যে তোদের স্বভাব।আজ থেকে তোদের প্রতি আশা ভালোবাসা সব মন থেকে উঠে গেল রে। তোরা সুখে থাক আরামে থাক তোদের স্বর্গরাজ্যে।,0,crime
ভাই আপনারে কত টাকা মিন্নি দিয়েছে মিথ্যা বলার জন্য ভাল হয়ে যাও,0,crime
আমরা প্রত্যেকটা প্রবাসী ও অনেক খুশি হয়েছি আমরা তাদের সবাই ফাসি চাই,0,crime
এই কয়টার জেলে দেওয়া দরকার,0,crime
ভিডিওর শেষের দিকে দেখা যাচ্ছে এক পুলিশ ভাইকে যিনি ক্যাপ পরিহিত একজনের সাথে এই বিষয় নিয়েই কথা বলছেন।। এই ঘটনায় ঐ পুলিশ ভাইটি সরাসরি জড়িত তাই বিচার সবাইর হওয়া উচিৎ ।,0,crime
এদের মুল হোতাদের ফাসি চাই।,0,crime
? থেকে দয়া করে একটু লক্ষ্য করুন মিন্নিকে প্রশ্নটা আপনার বিবেককে করে গেলাম ধরেন আপনার ভাই কিংবা ঘনিষ্ট কাউকে কেউ আপনার খুব কাছে থেকে মারধর করছে আপনি কি করবেন ? দাড়িয়ে থেকে অন্যদের মত তামশা দেখবেন ? নাকি নিজে কিছু করতে না পারলেও চিল্লাপাল্লা করে মানুষের সাহায্য অথবা ফোন করে নিজের আপনজনকে খবর দিবেন ? মিন্নি হলো সেইসব নারী যারা এই কুল আর ওই কুল দুইকুলেই ইচ্ছেমত ভুগ করে ! আপসোস ভাই পুরুষ নির্যাতনটা কেউ দেখেনা |,0,crime
আসসালামু আলাইকুম প্লিজ ভাই এই সমস্ত নোংরা ভিডিও আর ইউটিউবে বা ফেসবুকে ছেড়ে খালি খালি পাপী হয়েন না আশা করি আমার কথাটা আপনি মানবেন আসসালামুয়ালাইকুম,0,crime
এই ভিডিও থেকে স্পষ্ট বুঝা যাচ্ছে যে মিন্নি দোষী। আমাদের আর কিছু বুঝার নেই।মিন্নি কে ধরে আইনের আওতায় আনা হোক।মিন্নিই রিফাত হত্যার মুল আসামি।,0,crime
কথায় আছে না সঙ্গী গুনে লোহা জলে ভাসে আজ মিন্নি জন্য রিফাত দুনিয়া থেকে বিদায় নিল পুলিশ এখন ও ওকে করেনি কেন বুঝলাম না,0,crime
কিসের সাস্তি সরকারের সব মন্ত্রীরাইতু খুনী সন্ত্রাবাদ লুইচ্চামির সাথে জরিত এরাতু ইস্লামের পক্ষের নয় এরা ইসলাম বিরুদি,0,crime
আপনার কতাগোলা রাইট,0,crime
এদের জন্য দেশের এ অবস্থা এরা আবার দেশের বড় বড় পদে চাকরি করছে,0,crime
এতো কুপিয়েছে রিফাত শরিফ কে সে কিন্তুু মাটিতে পড়েনি সে হাঁটি ঐ দিকে ছলে গেল আল্লাহ জালিমদের উপর তোমার রহমত নাজিল করো কি যে কস্ট হচ্ছে ভাষায় প্রকাশ করতে পারছিনা ওদের সবগুলো কে কুপিয়ে মারা হোক। এটাই হবে সঠিক বিচার।,0,crime
দুঃখদায়ক কেউ বাচাতে এগিয়ে আসেনি কিন্তুু কেন আসেনি? সবাই জানে জে বণ্ড বাহিনী প্রভাবশালীদের ছত্রছায়ায় থাকে এর আগেও ওরা অপরাধ করে রেহাই পেয়েছে এবার ও তাদের কিছু হতোনা যদি ঐ সিসি টিভি টা না থাকত হয়তো সিসি টিভিতে ধরা না পরলে যারা তাকে বাচাতে আসতো হয়তো তাদেরকেই আসামি করা হতো,0,crime
তাকে বাঁচার জন্য দুটো গরম ডিম দিতে অনুরুধ করছি,0,crime
আলহামদুলিল্লাহ আমি ও মহ খুশি,0,crime
দরখাস্তে তার নম্বর দেওয়া আছে 😑,0,crime
পাপ করলে পাপের ফল তো পাবেই। এটাই তো সাভাবিক।,0,crime
ভিডিও না হলেই হলো মজাতো একটু করবেই হা হা হা। ভাই সে রকম কোনো বিচার হবেনা। ধন্যবাদ।,0,crime
ওকে দেখেই বুঝা যায় সে অপরাধী।,0,crime
জাদেখেআরকোনোদিন,0,crime
ফইন্নির কথা তে বুজার যে করছে তার ফাসি চাই।🤣🤣 মজা তুমি ও পাইছো আমি পাইছি।,0,crime
পরিবারের লোকজন কি বলবে বিবেকবান হলে বেচে থাকা,0,crime
আমার চ্যালেনটি করুন অনুরোধ রইল ♥,0,crime
আপনার কথায় যুক্তি আছে,0,crime
তোর পরিবারের কাছে নিয়ে যা তারা দেখে কিছু শিখুক,0,crime
অফিস কক্ষে বিছানা কেন সচিবালয় সহ দেশের অনেক কর্মকতার অফিস এর পিছনে বিছানা ব্যবস্তা কেন,0,crime
পরিবেশটা সুন্দর না কোন হইচই আছে,0,crime
অনেকমজাহবেতাইনা,0,crime
আললাহ আল্লাহ তুমি কই তুমি কি দেখ ওর বাবার কান্না তুমি আর কত জুলুম করতে দিবে তোমার কাছে বিচার নাই আললাহ,0,crime
আরে ভাই মিন্নি আসল অপরাধী,0,crime
মুরুখ,0,crime
জাদের সামনে এভাবে কুপিয়ে হত্যা করেছে ছেলেটাকে তারা মানুষের বাচ্চা না। আরে ভাই দু দিক দিয়েই রাস্তা জদি সবাই মিলে এগিয়ে আসতেন তাহলে হয়তো রিফাত ছেলেটা আজ বেছে জেত। জাক আর কিছু লিখি না। আল্লাহ রিফাতকে জান্নাত নসিব করুক। আমিন।,0,crime
টিবি চ্যানেল গুলু হলুদ সাংবাদিক।তাদের কথায় বিশ্বাস করবেন না। ক্যামারায় ধরা পরেছে মিন্নি জরিত।,0,crime
পুলিশ হেফাজতে পুলিশের হাতে জেল খানায় জেলার ও গার্ডদের হাতে অফিসে বসের হাতে বিমাণ বালারা ক্যাপটিনের হাতে ৷ সবাই জিম্মী ৷ তাই দেহ দিয়ে বসকে খুশী রাখছে ৷ কারণ বসরা ইচ্ছা করলেই কলমের খোচায় ওদের ক্ষতি করে দিতে পারো ৷ নারীদেরকে সর্ব ক্ষেত্রে বড় পোষ্টে নিযোগ দেওয়া হউক ৷ এসব কমবে ৷,0,crime
লোকটা একেবারে ঠিক বলছেন তোরা আগে দেখছ নাই হায়রে বাংলাদেশ কিছু বালার ভাষা নেই গজব আসবে এদেশে,0,crime
লুচ্চামির শেষ কোথায়,0,crime
নিজের অপরাধের তদন্ত নিজেই করবে,0,crime
জুতা পিটা করা উচিত।,0,crime
এখন আর মায়া কান্না করে কোন লাভ নেই নুসরাতের পরিবারের কেমন লেগেছিল ? তাকে আগুনে পুড়িয়ে মারা হয়েছে আসামিদের দ্রুত ফাঁসি দেয়া হোক ৷,0,crime
আমি ত ভাবছিলাম খোলা মেলা কিছু মাগার এইডা তো কোন ঘটনায় না😎😎😎,0,crime
দেখুন কি ভাবে খরগোশ বাসা তৈরি করে,0,crime
অাওমিলীগ ও তাদের নিয়োগ করা সবাই মিলে দেশেটাকে ইভটিজিং ও ধর্ষণের দেশ হিসেবে গড়েছে,0,crime
এইসব ক্লাব যে আছে বাংলাদেশের প্রোশাসন এবং সরকার জানে না প্রোশাসন জদি চায় সব খারাপ নেশা মাগিবাজি জুয়া খেলা সব ঠিক করতে পারবে কিন্তু করবে না।,0,crime
কিতা কইতাম ডিসি মিয়া শূন্য রানে বোল্ড হয়ে গেছে 😄😄😃😃কিছুদিন পর এটাও আড়ালে চলে যাবে,0,crime
মিডিয়া গো সত্য কথা লিখেন না কিল্লাই? হ্যারাতো লিখত্যাছে। কিন্তু আমনের পোলা প্যাইনে নুসরাত কে পুড়াইয়া মাল্লো ক্যান???,0,crime
অন্নের পাপকে ডেকে রাখুন আল্লহআপনার পাপকে ডেকে রাখবে,0,crime
আমার সুস্ত মস্তিষ্কের একটা ই প্রশ্ন মিন্নি কে কেন গ্রেফতার করা হয় না ?,0,crime
এটা কোন অবিনয় হল পারলে পতিবাদ করে দেখাও,0,crime
আসসালামু আলাইকুম আসুন আমারা সাবাই নিয়মিত পাঁচ ওয়াক্ত নামাজ পড়ি 🕌🕌🕌🕌🕌🕌🕌🕌 তাতে আমাদের সুন্দর জীবন হবে,0,crime
আমরা আজ লজ্জিত এ জাতী লজ্জিত,0,crime
রাজনীতির পাওয়ার দেখিয়ে কোন অপরাধ করবেন না,0,crime
এমন হাজারো কুকর্ম করছে অফিসার রা।ধরা পরলেই ইমাম সাব সাজার চেষ্টা।,0,crime
আমাদের জাতির পিতা শেখ মুজিবুর রহমান তিনি বেঁচে থাকলে কঠিন শাস্তি তাকে দিতেন। আর বাঙলার ইতিহাসে হয়তো এমন ডিসি কেনো কোন অসামাজিক আচরণ হইতে দিতেন না। হায়রে বাংলাদেশ!! কোথায় চলে গেছে!!,0,crime
এক জন ঈমানদাৱ বেক্তি কখনো এমন কাজ কৱবেনা এৱ জন্য দায়ি আমাদেৱ শিক্ষা সমাজ সংস্কৃতি বেবস্থা ধৰ্ম যাৱ যাৱ উৎসব সবাৱ বউ যাৱ যাৱ মেলামেশা সবাৱ উক্তিটা ঠিক এমন ধাৱাই এটা ত প্ৰকাশিত হওয়াই সভাই দেখতে পেয়েছে এমন লোক চুখেৱ আৱালে কতই না ঘটতেছে সৃষ্টি কৱতাৱ আইন থাকলে এমনটা হতো না সবাই একটু ভাবুন আমৱা মুসলিমৱা কোন পথে হাটতেছি আৱো সামনে আসতেছে সঠিক পথে হাটুন না পাৱলেও চেষ্টা কৱুন আমিন,0,crime
নুসরাত কে তো কাঁদতে ও দিস নি তোরা,0,crime
ওরা মায়ের বুক খালি করতে পারে ওদের মতো পশুরা বেঁচে থাকলে আরো কতো নুসরাত না ফেরার দেশে চলে যাবে এটাই ঠিক আছে ফাঁসি হচ্ছে ওদের এবার বুঝুক মৃত্যু কতটা যন্ত্রণার,0,crime
￰মহিলার বিচার চাই,0,crime
এটাই হচ্ছে আমাদের বাংলাদেশ না ভাংগা দেশ। যত রকমের ঘটনাই ঘটুক দিনের বেশি আর থাকেনা। দিন পরে সবাই ঠান্ডা হয়ে যাবে। কি বিচার কিসের বিচার সবাই ভুলে যাবে। এটাই আমাদের ডিজিটাল ভাংগা দেশ।,0,crime
সবাই কমবেসি খারাপ কাজ করে কারোটা প্রকাশ পায় কারোটা প্রকাশ পায় না তবে আল্লাহ আমাদের সবাইকে এই ধরনের খারাপ কাজ থেকে বিরত থাকার তওফিক দান করুক,0,crime
ভালের তদন্ত করবে,0,crime
শেখ হাসিনা সরকার প্রমান করলেন যে অপরাধী হোকনা কেনও সে যদি আওয়ামীলীগের কোন বড় নেতা হোকনা কেনও থাকে আইনের আওতায় এনে বিচার করা হয় যেমন ফেনির আওয়ামী লীগের সভাপতির বিচার দেখিয়ে দিয়েছেন শেখ হাসিনা সরকার যে কেউ অপরাধী হোক তার বিচার করা হবে,0,crime
অহন আমরা করলেই দোষ🤣🤣🤣,0,crime
এ রায়ে সবাই সন্তুুট প্রকাস করছি,0,crime
ওটা ডিসি না গরিব মানুষ শরিরে কোন কাপড় নেই ।,0,crime
স্বামি যখন দুনিয়া থেকে চেল গেল মিন্নি স্বামির সামনে দাড়িয়ে কেন কোপ খেল না জন ই মরে কি সমাস্যা ছিল।,0,crime
খুন খারাপি এরপর মিডিয়া থেরাপি এরপর গলায় মালা দিয়া জামিন বাহ নোবেলজয়ি নাটক 😡,0,crime
তোর বাচার মতো ব্যবস্থা আছে তোর স্যার কে পুলিশের কনস্টেবল এর চাকরি দিয়ে দুই কোটি টাকা কাবিন নামা দিয়ে তোদের দুইজনকে একসাথে করে করে বেতের বারি দিয়ে বিয়ের পরে দিলে তোর বাছার মতো ব্যবস্থা আছে । তোর যদি স্বামী মরে থাকে তুই গরিব একটা বেকার ছেলেকে বিয়ে করতে পারতি,0,crime
আমার মতে সব কলেজের সামনে মোতায়েন করা দরকার কারণ মারামারি সবসময় কলেজ ইউনিভার্সিটি তে হয়ে থাকে তাই মোতায়েন করাটা খুব প্রয়োজন মাননীয় প্রধানমন্ত্রীর কাছে আমাদের আকুল আবেদন কলেজ ইন ভার্সিটিতে আপনি মোতায়েন করার নির্দেশ দেন তাহলে মারামারি কাটাকাটি একটু হলেও কমবে,0,crime
তুমরা এগুলো করলে দোস নাই আর কএউ ভিডিও করলে দোষ,0,crime
বাংলাদেশের এখন এটাই অবস্থা। খমতার জোড়ে এদের কিছু হবেনা।,0,crime
তার বিচার আমার আদালতে তার ফাঁসি,0,crime
এইটা কেমন কথা মজা পাইলো দুইজন দোষ হইলো একজনের,0,crime
সবাই মিন্নির ফাসি চায় বাহ্ যারা প্রকাশ্য দিবালোকে কুপিয়ে চলেগেছে তাদের কে নিয়ে কিছুই বলেনা।,0,crime
আমি একটা জিনিস বুঝতে পারছি না এই ভিডিও তে যারা যারা ডিস লাইক করেছে তাদের ভাবা উচিত যে অপরাধ করলে সাজা হবে অপরাধ করার আগে ভাবা উচিত ছিল অপরাধ করেছে সাজা পেয়েছে এতে তো সবাই খুশি যারা ডিস লাইক করেছে তাদের ভাবা উচিত তাদের সন্তান কে যদি এই রকম নির্মম ভাবে হত্যা করা হতো তাহলে তাদের কেমন লাগতো,0,crime
স্যার এর কোনো দোষ নেই ্্্ কথাটির মাঝে রহস্য আছে।।। আর দোষ থাকবেই কিভাবে মজাতো দুই জনেই পাইছে্্্,0,crime
বাংলাদেশ আপনারা পারেন না এমন কোন কাজ নাই এখন অপরাধী রে মুক্ত করার জন্য মেয়েটাকে নিয়ে তামাশা করতাছেন এটা না করে পারলে অপরাধী কে ফাঁসিতে ঝুলান,0,crime
আমাদের বাংলাদেশে কোন সুস্ট বিচার নাই আমরা জনগনরাই পাড়ি অপরাধীদের শাস্তি দিতে না সেটা করবো কেন আমরা যদি শাস্তিই দেই তাইলে ভিডিও করবো কে সবাই পারে ফেসবুকে আইসা লাফালাফি করতে যাক আল্লাহ সবাইকে হেফাজদ করুক আমিন। আমরা চাই রিফাত সুস্ট বিচার পাক,0,crime
সব কিছুর সাথে আমার মনে হয় হাসপাতাল এর ও অনেক দায় আছে এই মৃত্যুর জন্য।কেননা সে অতটা জখম ও হয়নি যে মাটিতে লুটিয়ে ছিল।সে হেটেই প্রস থান নিয়েছে।ফেবুতে একটা পোস্টেও একজন বলছিল যে রিফাত এর অনেক বেশি রক্ত খরন হয়েছে ডাক্তার দের অবহেলার জন্য প্রথমে যে হাস্পাতাল এ নেওয়া হয় সেখানে তারা কিছুই করে নি। আর এই মিন্নি মেয়ে টা একবারের জন্য হাস্পাতাল ও যায় নি।সবকিছু বিবেচনা করে আইনের আওতায় নেওয়া হোক অপরাধী দের।,0,crime
এখানে জারা জারা ছিলো এবং জারা জারা তাকিয়ে তাকিয়ে দেখছে তারা সবাই অপরাধি আমি সবার বিচার চাই ওরা কয়জন ছিলো আর আমরা কতগুলা ছিলাম সবাই এগিয়ে আসলে ওরা পালানোর জায়গা খুজে পেতনা,0,crime
এই ভিডিও প্রথম দিন কেন প্রকাশ হয়নি,0,crime
যে কেউ অপরাধ করার আগে অন্তত একবার আপনার পরিবারের কথা চিন্তা করেন 😥😥,0,crime
যার হারায় সেই বুঝে হারানোর কষ্ট 😪,0,crime
হা হা হা আল্লাহ কি দুনিয়ায় আছি না মঙ্গলগ্রহে আছি। আমরা বিচার চাই।😂😂,0,crime
এসব নিউজ করে আর কি লাভ যদি দেশে সঠিক বিচার না থাকে,0,crime
রিফাত কে টেনে হিঁচড়ে নিয়ে যাওয়ার সময় মিন্নির স্বাভাবিক ভঙ্গিতে হেঁটে যাওয়া ভীষণ সন্দেহ জনক,0,crime
মিন্নী নাটক বন্ধ করুন,0,crime
তুই কিজাত সালাম দিছত,0,crime
মেয়েটি বলে দিয়েছে যে লিস্টে সব রাগব বোয়ালের নাম রয়েছে তাদের নাম উল্লেখ না করে মশা মাছিদের নিয়ে হৈ চৈ করচ কেন রিপোটাররা।,0,crime
নং আসামি মিন্নি,0,crime
মায়েদের ধর্ষণ করছি ধর্ষন ও খুন এদেশে মহামারি আকার ধারণ করেছে। বিবাহের ব্যাপারে বয়সের বাড়াবাডি বহু বিবাহের ক্ষেত্রে মাত্রাতিরিক্ত বিষয় আরোপ এবং নোংরা মিডিয়ায় যৌনতার ছড়াছড়ি ও সর্বোপরি নারীদের খোলামেলা পোষাকে অবাধ চলাফেরা আজ পুরুষদের যৌন কাতর করে পেলছে। হায়রে নারীদের পোষাক পরিচ্ছদ ! বোরকা পরে টাইট করে। নিতম্ব দেখানো দোলানো যেন এর উদ্দেশ্য। তেঁতুল হুজুরদের অবস্থা খারাপ। স্কিন টাইট জিন্স জামা কাপড় শরীরের প্রতিটি অঙ্গকে ফূটিয়ে তোলে যা সেক্স ফ্রি দেশের জন্য প্রযোজ্য। চলছে নেশা জাতিয় জিনিসের ছড়াছড়ি। নেশা খেলে কি ধর্ষণ করছে কে ধর্ষিত হচ্ছে কোন কিছুরই নেই ভেদাভেদ। ধর্ম ! ধর্মীয় অনুশাসন কোথায় ? ধর্ম প্রাণরা এবং ধর্মীয় প্রতিষ্ঠানও আজ সেক্স রোগে কাতর। ঘর ছেড়ে নারীরা অনেকেই অশালীন পোষাক আশাকে কর্ম ক্ষেত্রে গমন করছে । তাদের ছেলেমেয়ে ঘর সংসাব সামলাবে কে ? জাতির বিভেকের কাছে আজ প্রশ্ন। দেশ জাতি প্রজন্মের প্রতি নেই আমাদের ন্যূনতম শ্রদ্ধা ভালবাসাবোধ। আমরা নিজেদের নিজেদের সন্তানদের নিয়েই ব্যস্ত দৌড়াচ্ছি। আমরা যে যেখানে যা পাচ্ছি লুট করছি। অন্যকে ঠকাচ্ছি। আমরা লুটেরা। নিজেদের ক্ষমতা ও অর্থ সম্পদের জন্য অস্ত্র ও নেশা জাতিয় দ্রব্য তুলে দিচ্ছি ছেলেমেয়েদের হাতে। হয়ে যাক জাতি নেংটা ধর্ষিত পড়ুক লাশ ঘরে বাইরে সড়ক মহা সড়কে। বিশ্ব দরবারে হয়ে গেছি আমরা ধর্ষক খুনি ! ফলাফল আমরা মায়েদের ধর্ষণ করছি। খোরশেদ আলম,0,crime
রাতে কেন নয? রাগব বোযাল ধরা পড়বে বলে ?,0,crime
ভাই আসামিদের কিছুই হবে না কারন এর আগেও কয়েকটা খুন হইছিলো তারও বিচার হয় নায়।।আর এদের তো পিছনে উপর মহল আছে এক ওদের মাদক বিক্রি করা সহ সব কিছুর সেল্টার দিতো বর্তমান এমপির ছেলে অনিক আর এক আসামির খালু সাবেক এমপি দেলোয়ার হোসেন।।এখন সবাই ভাবুন বিচার হবে কিনা ????,0,crime
মেয়ে টার গেইম খুবই সুন্দর ছিল এক ডিলে দুই পাখি,0,crime
কেউ,0,crime
অনেকদিন পরে শেখ হাসিনার একটা সালাম দিলাম এরকম সরকারের দরকার,0,crime
সাংবাদিক রাও পাগল।। গরু কে জিজ্ঞেস করে গরু হাল চাষ।।উপরে মহলে যায়তে হবে,0,crime
মনটা আমার সান্তি পেলো।।। আজ দেখলাম বাংলার বোকে সঠিক বিচার পেলো।।,0,crime
এরকম কান্না তো নুসরাতের মা ও করেছিল এবার বুঝ কেমন লাগে সন্তান হারানোর কতটা কষ্ট,0,crime
যতগুলো মানুষ দাড়িয়ে আছে শুধু দর দর বলে চিল্লায়লেও চলতো কাছাকাছি না গেলেও দৌড়ে পালাতো,0,crime
ঈ ভভ ম,0,crime
অবশ্যই মিনি এবং তার অন্যান্য খুনিদের বিচার চাই,0,crime
মহিলা জরিত,0,crime
এই ভিডিওতে মিনন্নি সবতার বানানো কথা,0,crime
একটি দুষ্ট মেয়ের জ্ন্নে দুই মায়ের বুক খালি হল তাই এই মেয়েকে ফাঁসি দেওয়া হউক। ভারত থেকে বলছি।,0,crime
আমরা সবাই মুখোশ পরিহিত।মুখোশ টা সরালেই আসল চেহারা বের হয়।,0,crime
ভিডিওটি বার দেখলাম এবং বুঝতে পারলাম মাত্র দুটি রামদার সামনে শত শত মানুষ কত অসহায়।,0,crime
যারা নুসরাত কে তনু কে এবং রিফাত কে নির্মম ভাবে হত্যা করেছে তাদের কে জনগন এর সামনে কুকুর এর মত গুলি করে মারতে হবে,0,crime
এখানে সাধারণ মানুষ ধরা পরলো তাদের দেখায়।বড় বড় লোকগুলো কয়🤣,0,crime
মাইয়ার দালাল,0,crime
এই ভিডিও থেকে শিক্ষা নেওয়া উচিত যে যেকোন সময় যেকারো এমন অবস্থা হতে পারে। তাই যদি আপনি অন্যের বিপদে এগিয়ে না আসেন একসময় আপনার বিপদেও কেউ এগিয়ে আসবেনা! আর এটাই বাস্তবতা সময় থাকতেই সাবধান হওন সচেতন হওন মহান আল্লাহ পাকের শ্রেষ্ঠ মাখলুক মানুষকে ভালোবাসতে শিখুন আল্লাহ পাক আপনাকে ভালোবাসবেন।✌,0,crime
সমস্ত ঘটনা রিফাত এর স্ত্রী মিন্নির পরিকল্পিত মনে হচ্ছে,0,crime
একেই বলে অবৈধ সরকারের জেলা প্রশাসকের অবৈধ লীলাখেলা। কয়জন এমনটা দেখাতে পারে। আর একেই বলে প্রেমে মজিলে মন কিবা ঋষি কিবা ডোম এহলো বাবা এলজাব্রার থিওরি প্লাসে প্লাসে প্লাস সুতরাং অবৈধ অবৈধ অর্থাৎ এবং এই দুই মিলে তো প্লাস হবে তাইনা এই থিওরি আপনাদের মনে আছে নিশ্চয়ই। এখন এমন ঘটেছে যাকে বলে কিনা মহা সংযোগ। তাইতো এখন এদের বিয়ে পড়িয়ে দিলেই তো সব সমস্যার সুস্ঠ সুন্দর শান্তিপূর্ণ সমাধান হয়ে যায়। মাননীয়া প্রধান মন্ত্রী ছাড়া তো কোন সমস্যারই সমাধান হয়না । এবারও তিনি নিশ্চয়ই রাষ্ট্রীয় সরকার প্রধান গুরুজন হিসাবে মহা ধুমধামের সাথে এদের মধ্যে বিয়ের ব্যবস্থা করবেন। তবে এবার নিশ্চয়ই আমরাও নিমন্ত্রন কার্ড পাচ্ছি তো,0,crime
আপনার অভিযোগ সত্যি ।,0,crime
পরিবেশটা সুন্দর না 🙄কোনো হইচই আছে 🙄আমি কি কাউকে গালি দিসি কারো বিরুদ্ধে বলতেসি 🙄এরপরেও দেখবেন একদল লোক বলবে তাহেরি বালা না 😏😏আমিও বলি আমি তো বালা না বালা লইয়া থাইকো🥺🥺কতা কি কিলিয়ার নাকি বেজাল আছে🤔একেক সময় একেক কতা ছাড়ি আর সেটা ফেজবুকে হিট হইয়া যায়🥴🥴চিল্লাইয়া মার্কেটে ফাওন যাইবো 🙄🙄চা খাবেন দেই একটু 🌚ঢেলে দেই 🤢 ফাম দিস না ফাম দিস না 🤣 আমাকে বার বার কমেন্ট করতে বাধ্য করো এসব পোস্ট দিয়ে 🌚🌚,0,crime
ধন্যবাদ মাননিয়া প্রধানমন্রী আপনাকে । আপনি শক্তহাতে এসমস্ত অপরাধীকে দমন করুন পুরোদেশ আপনার সাথে থাকবে। আল্লাহ তা আলা আপনার হাতকে আরো শক্তিশালী করুক।,0,crime
এই ভিডিওতে বুঝা যায় মুন্নি এই খুনিদের সাথে জড়িত আছে,0,crime
আহারে তোমার সব কিচু সবাই দেখছে,0,crime
সালামুআলাইকুম প্রথম অনুরোধ রইল আমার মেসেজটি পড়ার জন্য পৃথিবীর বুকে সব কিছুরই ধর্ম আছে কর্ম আছে পৃথিবীতে সব কিছুরই তার সাজা আছে এটাও সঠিক এলাকায় যে কোন জিনিসটা হয়ে গেল এটা কি কোন সাজা হবে না এটাতো তার চেয়ে বড় কিছু এটা নিয়ে আমি আইনজীবীর কাছে আদালতের কাছে প্রার্থনা করছি কি সাজা দেওয়া যায়,0,crime
এই ভিলেনদের দ্রুত ফাসি কাযকর করা হোক। প্রথম ফাঁসি দেওয়া হোক রিফাত ফরাজি কুত্তার বাচ্চাটার তারপর ওর সহযোগিদের যারা রিফাত কে জাপটে ধরেছিল। এরা প্রত্যেকেই সম অপরাধী এদের ফাঁসি না হলে বুঝবো এ দেশে কোন আইন নাই। বুঝবো এ দেশে মানুষ বাস করে না মানুষ নামে জন্তু জানোয়ার বাস করে।,0,crime
মিন্নি হসহায় আপনাকে ধন্যবাদ,0,crime
সালামু আলাইকুম ভাই আপনাদের ভিডিওটা কিছু অংশ ভুল হয়ে গেছে,0,crime
হায়রে মানুষ ছেলেটাকে যখন কিল ঘুসি মারছিলো তখন সবাই দারিয়ে দেখছিলো যখনি অস্ত্র দিয়ে আঘাত করা শুরু করলো তখনি সবাই দৌরে পালালো।,0,crime
মিন্নি এটা কি করলি!!!একটা নিরপরাধ ছেলে মরে গেলো তুই জুতা খুঁজিস! আরে এমন সময় তোর গায়ে ওড়না না থাকলেও তো স্বামীকে আগে ধরতি।তোর জুতার অনেক দাম মনে হচ্ছে।এখন এই কুলেরটাও গেলো ওই কুলেরটাও গেলো।এবার এই জুতা নিয়া কাটাস বাকি জীবন।মনে রাখিস উপরে আল্লাহ আছেন।কেউ হয়তো তোর জারিজুরি বুঝবে না কিন্তু ওপারে রেহাই পাবি না।,0,crime
হাহাহা দোষ কি খালি তার নাকি মেয়ের আছে,0,crime
আসলেই এটা জাতীয় জিজ্ঞেস মিন্নী! হায়রে নারী খুব কষ্ট হয়,0,crime
গ,0,crime
ফাসী চাই,0,crime
মসলা,0,crime
মিন্নিরে সবাই মিলে বাস দেওয়া দরকার তার এত স্বামি কেন চাই বাট বাকিদের ফাসি,0,crime
মিন্নি সরাসরি জড়িত অার কি প্রমাণ লাগবে।,0,crime
সবাই দেখবেন। আশা করি ভাল লাগবে।,0,crime
স্বরাষ্ট্রমন্ত্রী ও বলছিল ঘন্টার মধ্যে সাগর রুনির হত্যার বিচার হবে তার পর🙄🙄 বাকিটা সবাই জানে,0,crime
নিজের ছেলে মেয়ে সোনার টুকরো আর পরের ছেলে মেয়ে পরিত্যক্ত কয়লা? ওই কুকুরদের যেন তাড়াতাড়ি ফাঁসি কার্যকর হয়।,0,crime
বর্তমান সরকারের আওতায় নেতাকর্মি সহ সবাই তার নিচের পোস্ট এর মেয়েদের সাথে এসব করে। এসব ক্ষেত্রে মেয়েরা অসহায়। চাকরি বাঁচানো বড় দায় হয়ে পরে। সেক্স না করলে।।,0,crime
খুনিদের বিচার চাই কঠিন সবাইকে,0,crime
ছি ছি ছি নিলজ্জ বেহায়া। একটা বালি পরিমাণ লজ্জা বলে কিছু নেই। ধিক্কার চাকুরী দাতার কাছে ইজ্জত বিক্রি,0,crime
এসব এর সাথে সরকারের প্রভাবশালী নেতারা জরিত নিশ্চিত। তাদের বিচার কে করবে। যারে দিয়ে ভূত ছাড়াবে তারেইতো ভূতে ধরে রাখছে।,0,crime
আজ পর্জন্ত কোন তদন্তের রিপোর্ট জনগন দেখেনি।।।,0,crime
এরকম বিচার হলে এদেশের মা বোনদের ইজ্জত নিয়ে আর ছিনিমিনি করবে না।,0,crime
যদিও মিন্নির ফাঁসি দিতে হবে,0,crime
🎺 এজন্যই আসুন আমরা সন্তানদের সৎপথে চলার আদেশ এবং অসৎ পথ থেকে বিরত থাকার নির্দেশ দেয় যেন আর কোন মায়ের আহাজারী শুনতে না হয় ⤵️ অপরাধী নয় অপরাধ কে ঘৃণা করুন ❌,0,crime
এটাই বাঙ্গালী।।।,0,crime
রায় শুনে খুশি হলাম কিন্তুু সেখ হাসিনা এই রায় যদি বদলায় আপনি গদি ছাড়তে হবে বাংলার জনগন এখন সচেতন,0,crime
আই রে না সেই আওয়ামীলীগ করে না সমস্যা নেই কারন হাসিনার কাছে ধর্ষণ বাহিনী আছে এর মধ্যে একজন,0,crime
মিন্নি বাবা কুখ্যাত সোতখোর তারে হুজুর বানাইলেন আর বাচ্চা কাহিনী কুই,0,crime
এসব ভিডিও কি মানুষ নেটে ছাড়ে গেলু ছাড়া মানুষ কারো মাথায় কি গেলো নেই হাইরে মানুষ,0,crime
ভাই খুব ভাল কথা বলেছেন,0,crime
মিন্নি কে রিমান্ডে আনলেই সব ঘটনা প্রকাশ হবে আমি মনে করি,0,crime
বড় মাছ গুলা কই ভাই তাদের দেখাতে কি ভয়পান নাকি।,0,crime
ফাঁসি দিয়ে দে এন,0,crime
কথা বলা শিখো।,0,crime
কেমেরার বাহিরে এমন অনেক ঘটনা ঘটে যা অার প্রকাশ পায়না রাজনীতি নামের দূর্নীতিবাজদের ছত্র ছায়ায় এবং প্রশাসনের অর্থ গ্রহনে অপরাধীরা বেচে যায় এবং অপরাধ বাড়তে থাকে৷ পাগল ব্যতিত সবাই এই ভিডিও দেখে বুঝবে মিন্নি ঘটনার সাথে জড়িত৷মিন্নি সহ এ ঘটনার সাথে জড়িত সকলের ও নয়ন বন্ডদের যারা তৈরী করে তাদের মুখোস খুলে তাদেরও বিচার দাবি করছি৷,0,crime
বলার ভাষা হারিয়ে ফেলেছি!,0,crime
মিন্নি রিফাত ভাইরাক ছিলো প্রিয়া সাহা তার জায়গা নিলো প্রিয়া সাহাকে সবাই ভুলে গেলো কল্লাকাটার উদ্ভব হলো কল্লাকাটা থেমে গেলো ডেঙ্গু মশা জন্ম নিলো ডেঙ্গু মশার দিন শেষ ডেলে দিই বাংলাদেশ রুমে ছিলো এসি আড়ালে ছিলো সিসি আহারে বেচারা ডিসি দেশবাসী দিচ্ছে ছিঃ ছিঃ,0,crime
ডিসি সাহেব সাধনার সাথে যা করেছেন তার বিচার আইনের কাছে দিলাম।কিন্তু আমাদের মতো সাধারন জনগনের রেপিডেন্স আর টেক্সের টাকায় কেনা টিসুর যে অপব্যবহার করলেন তার বিচার কে করবে।লজ্জা শরমের বালাই দিয়ে ঘরে উপযুক্ত মেয়ে এবং সুন্দরী স্রী রেখে কেমনে এমন বেহায়াপনা করলেন।এটা কিন্তু তাদের দোষ না। এটা আসলে তারিখে দিবা রাত্রির পরিশ্রম করে ভোটার বিহীন এই অবদ্য সরকার কে ক্ষমতায় বসানোর উপহার সরুপ। তাই তো এই গোপন কক্ষ আর এই কক্ষে সাধনাদের মতো হাজার ও নারির খোশ আমদেদ। জানিনা সামনের দিন গুলোতে সমাজ তথা রাষ্ট্রের উচ্ছ পর্যায়ের মানুষ গুলো এই জাতিকে আর ও কত সুন্দর সুন্দর মিয়া খলিফা বা সানি লিওন মার্কা ভিডিও উপহার দেন।দেশের এত বড একটা পদের মানুষ এমন একটা কাজ করলো আর দেশের নারীবাদি সুচিল সমাজ আজ চুপ।কিছু বঝলাম না ওনাদের ও কি দুর্বলতা আছে নাকি যদি তাই না হয় কেন তারা নিরব দর্শক।নাকি ডিসি সাহেব শিক্ষিত সমাজের এক বলে ওনাদের লজ্জা করতেছে।হায়রে দেশ হায়রে দেশের রাষ্ট্র যন্র।হায়রে আমার দেশের মানুষের বিবেক।আজ প্রতিবাদ না করলে নাই কিন্তু এ দিন এই স্বাধীন বাংলার ভবিষৎ প্রজম্মের কাছে জবাব দিতে হবে।সব সাধুরা বেল তলায় জায় না।,0,crime
সারা দেশেই নারীরা কর্মক্ষেত্রে উর্ধ্বতন কর্মকর্তার ভোগের বস্তু। অবশ্য কিছু পতিতাও আছে যারা নিজেই নিজর দেহ বিলিয়ে দেয়। এমন নিয়ম প্রয়োজন যে নারীদের কর্মক্ষেত্রে কোনো পুরুষ থাকতে পারবে না আাবার পুরুষদের কর্মক্ষেত্রে কোনো নারী থাকতে পারবে না,0,crime
মিন্নির দোষ আছে তা প্রত্যেকেই বিশ্বাস করে।কিন্তু ছেলেরা কেন এই ভেজাল আলা মেয়েদের বিয়ে করে।আবার তার পেছনে দৌড়ায়!!!দেশে কি ছেড়ির অভাব।জাতের মেয়ে কালো ভাল জাতের ছেলেও কালো ভাল।ছেলেরা অভিনয় করা ন্যাকামি করা লুতুপুতু করে চলা মেয়েদের খুব পছন্দ করে।কেন রে ভাই।যে গেছে ওর পেছনে লাত্থি মেরে তাড়া।ওর পেছনে কি।যে আরেক জন ছেড়ে তোকে চায় সে আরেক জনের জন্য তোকেও ছাড়তে পারে।দোষ সবার।,0,crime
হাহা রিয়েক্ট নাই কেন ইউটিউব এ 😝🤪😂😂😂🤣,0,crime
এবার বুঝতে পারলাম মামলা থাকা সত্ত্বেও কিভাবে জামিন পেয়ে বেড়িয়ে আসে এদের সাথে নেতা দের হাত আছে,0,crime
রিফাত হত্যার মূল আসামি তার স্ত্রী মিন্নি,0,crime
মিন্নির কোনো অপরাধ দেখা যাচ্ছে না,0,crime
একেবারে পালতু বাস্তবের সাথে কোনো মিল নেই বাস্তবে মিন্নির দোষ গুলো ও পরিকল্পনা গুলো তুলে ধরা হয়নি,0,crime
পুরো দেশবাসী এখন জানে মিন্নিই হলো এই হত্যার মাস্টার মাইন্ড। কিন্তু অবাক বিষয় আসল খুনীকে মিন্নি এখনো ইচ্ছে করেই গ্রেফতার করা হচ্ছে না। মিন্নি কি দেহ দিয়ে উচ্চ মহলের কাউ কে হাত করে রাখছে ???,0,crime
ওরে অামাকে কেউ ধর অার কি দেখমু,0,crime
এ দেশ আর কি দেখতে চায় আমরা আর কিছু দেখতে চাই না অনেক দেখেছি আর তদন্ত তদন্ত করে কি হবে আমারতো মনে হয় তদন্ত করে তাকে পুরস্কৃত করা উচিত কারণ সে আমাদের সমাজের একটা জ্বলন্ত প্রমাণ যে সরকারি কর্মকর্তারা অনায়াসেই তাদের কার্যালয় বেডরুম বানিয়ে নারী কর্মকর্তাদের নিয়ে আমোদ ফুর্তি করে এদেশে তদন্ত করে কিছু হবে না খুন করেও মানুষ মাফ পেয়ে যায় তারপর তারপর তো ইচ্ছাকৃত যৌনাচার এটা আসলে কোন বিচার হওয়া উচিত না কারণ দেশ তো আর এখন বাংলাদেশে নয় আর মুসলিম দেশ ও নাই আমার মনে হয় ডিসি সাহেবের এই সেক্সুয়াল ভিডিও দেখে সরকারের সেক্স উন্মুক্ত করে দেয়া উচিত জাতির প্রত্যাশা এটা কারণ আপনি যদি বিচারই না করতে পারেন তাহলে সমর্থন করেন তাও তো জাতি আপনাদের কাছ থেকে একটা সিদ্ধান্ত পাইল তবে তা না হলে এই তদন্ত নামে বছরের পর বছর শুধু তদন্তই পড়ে যাবে আজ যে ভদ্রলোক তদন্ত করবে সেই ভদ্রলোককে যদি ডিসি সাহেব থেকে লাখ টাকা পকেটে ঢুকিয়ে দেন তাহলে তদন্তের সবই মিথ্যা প্রমাণ হবে আরে বাবা এ দেশে কি আইন আছে নামেমাত্র আইন কিন্তু আমাদের দেশে আইনের শাসন নেই বললেই চলে,0,crime
বিচার হওয়া উচিত,0,crime
ইসলাম অনুযায়ী বিবাহিতরা অনৈতিক কাজ করলে তাদের পাথর মেরে মৃত্যুদণ্ড কার্যকর করতে হবে।এই আইন থাকলে সমাজে এতো অনৈতিক কাজ করার সাহস পেতো না কেউ।জঘন্য মহিলা অনৈতিক কাজ করার সময় স্বামী সন্তানের কথা মনে ছিলোনা তোর মরে যাওয়াই উচিৎ সাথে ওই শয়তানটারও।শুধু অনৈতিক কাজ নয় দুইটা ফ্যামিলির সাথে প্রতারণা করা হয়েছে।যদিও দেশের আইনের প্রতি বিন্দু মাত্র বিশ্বাস নাই।দেখা যাবে শেষমেশ তারা নির্দোষ প্রমাণ হবে।আর আমরা জনগণ যা দেখেছি সব বানোয়াট জাল ভিডিও! আল্লাহ্‌ তো আছেন।তিনি উত্তম বিচারক।,0,crime
আওয়ামীলীগ এর নেতারা যা বলে না হেসে পারা যায় না মিথ্যা বলতে বলতে এখন কি বলবে খুজে পায় না,0,crime
চ্যানেলটি সাবস্ক্রাইব করে পাশে থেক।,0,crime
এই সব মেয়ে দের কঠিন বিচার করা দরকার।,0,crime
কিছু সাংবাদিক আবার এরও কোম আমরা আরো আগে দেখি ছি কিছু হয় নি,0,crime
এখানে অনেকে মিন্নিকে দোস দেয় কেনো বুজি না।৷,0,crime
ভাই আপনে জেটা বলেছেন সেটা ঠিক আছে সহজ হিসাব টা পুলিশ কেনো বুজেনা,0,crime
হা‌সিনা তু‌মি চিরজী‌বি হও। সরকারী অ অ‌ফি‌সে ঘোষ বন্দ কর। বি‌শেস ক‌রে ঘোষ খায়,0,crime
তোমাদেরকে এখনো সরকারের পুরস্কার দেয় নাই,0,crime
আসল অপরাধী ধরা পড়লে মিন্নির দোষ তো প্রকাশ পাবেই,0,crime
যে তিনটা সরাসরি খুনি অংশগ্রহণ করেছে তার মধ্যে একটা তো ক্রসফায়ার হয়ে গেছে বাকি দুইটা কে ক্রসফায়ার দিয়ে অন্যদের এবং যারা জড়িত ছিল তাদেরকে তদন্ত সাপেক্ষে আইনের আওতায় আনা হোক। আমার মনে হয় এই খুনের পিছনে তার স্ত্রী ও জড়িত ছিল।,0,crime
তাইলে দোষ কার মজা তো দুই জন ই পাইছো,0,crime
ভিডিও প্রমাণিত হয়েছে এটা সত্য ঘটনা,0,crime
? থেকে,0,crime
মিন্নি অবশ্যই এই বিষয়ে কিছু জানে এটা আমি এর সাথে বলছি মিন্নি কে রিমান্ডে নেওয়া হোক প্রতিবাদ জানাই,0,crime
বাহ তোতা পাখির মতো শিখানো বুলি এগুলো কি আপনার শিখানো ভাই এখন দেখলাম পুরো পরিবার অভিনয় করতে পারে ওয়াও,0,crime
এই সব লোক যতো দিন ধাইতে থাকবে ততো দিন এমনি হবে,0,crime
খুব তারাতারি রায় কার্যকর হবে আশা রাখি,0,crime
এখন বোরকা পরা এতো দিন ছিলো সদরঘাট লঞ্চ টার্মিনাল এখন বিমানবন্দ বাহ দারুণম্যাচে খেলেছেন,0,crime
মিথ্যা কথা বলে পুলিশ।,0,crime
এই সব লোকদের ফাঁশিরকাট ঘরায় দারকরান হোক এই দাবি জানাই আমরা??,0,crime
তোমার আর ডিসি কোনো দোস নাই সব দুস তোদের সের দুস তাই না সবাই শুনুন তাদের দুজনের কোনো দুস নাই সব দুস ঐ ঐ সি সি কেমরা দুস,0,crime
দুই জনে ই সমান অপরাধী সুতারাং দুইটারে পাথর নিক্ষেপ করে মারা হোক সাক্ষী প্রমান সব আছে,0,crime
তাহলে কোটি টাকা খরচ করে সিসি কেমরা বসিয়ে কি লাভ সিসি কেমরা যদি মিথ্যা প্রমাণিত হয়,0,crime
মনে হয় মেয়েটার চাল এটা জাতে করে ডিসিকে বিয়ে করতে পারে,0,crime
এতো দিন কোথায় চিলো এই ভিডিও,0,crime
তোদের মতো আরো এই রকোম মেয়ে থাকলে তাহলে হাজারো রিফাত মারা যাবে তোকে রিমান্ডে দেওয়া উচিৎ । খারাপ মেয়ে তুই।,0,crime
এই ভিডিওতে টা মিনিট সেকেন্ড থেকে টা মিনিট সেকেন্ডের ভিডিও টুকু কেটে দেওয়া হয়েছে কেন? ইউটিউবে অন্য একটা ভিডওতে দেখলাম এ সময় রিফাত চলে যেতে চাচ্ছিলো কিন্তু মিন্নী বাইকে না চড়ে কলেজের মধ্যে চলে যায় মিন্নী কি ইচ্ছা করেই রিফাতকে আটকে রাখলো? বিষয়টা খতিয়ে দেখা দরকার।,0,crime
নিশ্চয়ই নামাজ সকল অন্যায় অবিচার অত্যাচার খারাপ বাজে কাজ থেকে বিরত রাখে,0,crime
আল্লাহর করা নিয়মের বাহিরে কিছু করলে তার পরিনতি এমনই হবে,0,crime
আমি জানিনা যে এই ভিডিও টা সবাই কি ভাবে আর কতটুকু মনোযোগ দিয়ে দেখেছেন। তবে এই ভিডিও টা দেখে বোঝা যায় যে মিন্নির হাত আছে। আর পরিকল্পিত হত্যা করেছে। মিন্নির ফাসি দাবি করছি। আর এই ভিডিও টা এতো দিন সারা হয়নি কেন।,0,crime
আরে বাঙ্গালি বলে কথা। এই হলো আমাদের সরকার ব্যাবস্থা। এই হলো নারির ক্ষমতায়ন ।আর যে কোন ক্ষেএে নারিদের প্রাধান্য দেয়ার একমাএ কারন।,0,crime
খুনিদের বিচার হবেতো,0,crime
মেয়েটির জন্য আজ এই পরিনতি,0,crime
যখন রাফি কে মারছে তখন কলিজা কাঁপে নাই তখন ভাবো নাই যে এর সাজা একদিন পাইতে হবে তাজা মানুষ কে কিভাবে পুড়িয়ে মারছে তখন মেয়ে টার কষ্ট হয় নাই??????? আজ বোঝো,0,crime
সাবিবর,0,crime
মিন্নির দোষ,0,crime
ওরে চামরার জুতা দিয়ে পিটানো দরকার,0,crime
মারা সময় কেয় আগাই নাই মরার পরে সবাই এখন আগাবে ভাই বলবে রিফাদ নাই আমি আছ বন্ধুরা বলবে রিফাদ নাই আমরা আছি এটাই বাস্তোব কি বলে,0,crime
আল্লাহ যানে কত জন পুরুষের বৌ খাইছে। তাদের প্রকাশ্যে বিচার হলে ভাল হবে।,0,crime
সুন্দরি মেয়েদের কপালে জুটে গুন্ডা বর,0,crime
ওনার সাক্ষাৎকার নেওয়া দেখে আমার অনেক হাসি লাগছে এটা যদি কোন সাধারন মানুষ করতো কিভাবে সাক্ষাৎকার নিতে বাংলাদেশের সাংবাদিকেরা,0,crime
মিন্নিও দায়ি বুযা যাচ্ছে এই ভিডিও তে?,0,crime
চলতে দিন,0,crime
এই খুনের সবচেয়ে বেশি জড়িত মিন্নি। এই মেয়েই এই কাজ টা করিয়েছ এই ভিডিও তার প্রমাণ সরুপ।খুনিদের সাথে সাথে মিন্নির ও বিচার চাই,0,crime
ধন্য বাদ সওি গঠনা,0,crime
লাপনাই দেকবি ফাসি দিলে পরে,0,crime
মিন্নি এদের সাথে জরিত,0,crime
ওসি মোয়াজ্জেম কই তার কি কোন বিচার হবে না??,0,crime
আমার একটা প্রশ্ন আছে। এই কেসিনুর আড্ডায় শুরু থেকে শেষ পর্যন্ত যারা এসেছে এদের সবাইকে কে শাস্তি দেয়া হোক। শুধু এদের কেন? র‍্যাব পুলিশ নেতা সাংবাদিক সরকারি আমলা সবাই যারা এখানে এসে জোয়া খেলেছে।,0,crime
মিন্নির যেন ফাশি হয় আর ফাশি যদি না হয় তাহলে মিন্নির যেন যাবোত জীবন কারা দন্ড যেন হয়,0,crime
দালাল,0,crime
আমি মনে করি আমরা দাহি কেনো না। আমাদের সবার সামনে একটা মানুষকে মারে? আর আমরা তাকিয়ে দেখি। আমি বলি তোদের চার পাশের মানুষ গুলো দারায় ভাই টা মারা গেছে। তোরা কেনো যে মুরগির কলিজা নিয়ে বেচে আছিস।,0,crime
মিন্নিকে ফাসি দিলে। সবমেয়েরা একাজ থেকে দুরে থাকবে। সরকার কে।বলি মিন্নিকে ফাসি দেয়া হোক। না দিলে এরকম কাজ আরো বেসি হবে।,0,crime
এই মহিলা কে গ্রফাতার করা উচিত আমি মনে করি,0,crime
ইস অনেক কষ্ট হয় বিডিও টা দেকলে,0,crime
তিনি সরল মনে এমনটি করেছেন।এতে সমস্যা কি😎😛,0,crime
পরকীয়া পেম করলে ভাল ভাল ছেলেদের এমন হয় আমি মনে রিফাতে বউয়েও দুষ বেশি,0,crime
হা হা রিএক্ট থাকা উচিত ছিল।।।,0,crime
ঠিকই আছে বিচার এদের কে নিয়ে আলোচনা সমালোচক করা অনুচিত ওকে,0,crime
মিন্নি কে আগে ফাঁসি দেওয়া উচিত কারণ তার স্বামীকে যখন সবাই ধরেছিল তখন সে কিছুই করিনি যখন তাকে কোপানো হচ্ছিল তখন সে নাটক করেছিল,0,crime
তদন্ত করছে তার নিন্মস্ত কলিক বিষয়টা হাস্যকর।,0,crime
নয়ন বন্ডদের কে জানাল যে রিফাত শরিফ কলেজে আসবে? মিন্নী ছাড়া অন্য কেউ কি করে জানল যে রিফাত শরিফ তাকে নিতে আসবে। আবার বাইরে থেকে ভিতরে দৌড়ে চলে গেল কেন? কেমন যেন লাগছে। আল্লাহ তাআলা ভালো জানেন।,0,crime
নাটক,0,crime
স্বামীর সাথে ডিভোর্স হয়ে গেলেও তাকে হত্যা করার কথা ভাবা যায়না কি করে এই মেয়েটা পারলো!!!!,0,crime
ভিডিও টা ডিলিট কর তা না হলে তুমাকে গ্রেফতার করা হবে,0,crime
হা হা হা মজা পাইলাম তদন্ত 😀,0,crime
হা হা হা এই হইলো দেশের অবস্থা আল্লাহ আমাদের কে হেদায়েত দান করুন আমিন,0,crime
এখানে তদন্ত করার কি আছে কেউ জানলে জানাবেন।,0,crime
জেলা প্রশাসকের কথা সবাই বলেন কিন্তু মেটি কাপড় খুলেছে তাঁর কথা কেউ বলছি না তাহলে সবাইকি মহিলার পরখ করতে ছেন,0,crime
কত প্রমান লাগবে তার কাপুর নস্ট করেছে কিনা সেটা কি তদন্ত কমিটি তদন্ত করবে,0,crime
সোনা কাঠি দাও 🤗,0,crime
পৃথিবীর সব মানুষের কিছু না কিছু বিশেষ গুন থাকে। আর মিন্নির বিশেষ গুন হচ্ছে এর অভিনয়। এর গুন নয়ন বা রিফাত কেউ ধরতে পারেনাই যার ফলাফল এই ঘটনা। তবে এবার যে মিন্নি হেরে গেছে এটি নিশ্চিত।,0,crime
কেনে এই মেয়েকে মেরে পেলেচি কি অপরাদ করেচিল,0,crime
জামালপুরের ডিসির সাথে সেক্স ভিডিও পুরা মিনিট দেখতে ক্লিক করুন,0,crime
গান গেয়েই তো সাধনাকে পাগল করেছেন,0,crime
এই মেয়ের কারনে আজ এই ছেলের অবস্তা এই মেয়ে ও জড়িত আছে ৷ আমার মনে হয়,0,crime
ভাই ধরা পরলে চোর আর না ধরা পরলে সাধু তাই সবাই নিজের দিকটা চিন্তা করেন,0,crime
খায় দায় কাম নাই না,0,crime
এরখম জঘন্যতম অপরাধ দেশকে খারাপ থেকে আরও খারাপের দিকে নিয়ে যাবে।এই বয়সে এরখম খারাপ কাজ কীভাবে করে এইসব পতিতা মহিলা ও পুরুষ সামাজিক পরিবেশ ধ্বংস করে দিচ্ছে। এদের বিরুদ্ধে ইসলামিক আইনের আওতায় আনা হোক।,0,crime
হায় রে দুনিয়া আল্লাহ তুমি সবাই কে হেদায়েত করো।।।।,0,crime
ঐই মহিলা বলতেছে বিচার চায় কার বিচার চায় তাহলে সব কি মিথ্যা মহিলা আরও বলতেছে ওনার নাকি সন্তান আছে যখন এগুলা করে তখন এই চিন্তা কোথায় ছিল,0,crime
এই মিন্নির সাস্তি না হলে ফাসি না হলে হাজার হাজার মিন্নি পয়দা হবে সবাই অান্দোলন করেন,0,crime
বাহ ইউটিউবেও চলছে,0,crime
মেয়েটির মাথায় চুল নাই ভাই তাই তিনি হিজাব পরেন। কে এই ডি‌সি স্যা‌রের সাধনা অনেক সাধনার প‌রে অন্যর সহ‌যোগীতায় জামালপুরের ডিসির সাথে অপত্তিকর ভিডিও তে ভাইরাল হওয়া সেই অালোচিত ডিসি অফিসের পিয়ন সানজিদা ইয়াসমিন সাধনা কে নিয়ে অনেক কৌতুহল। সানজিদা ইয়াসমিন সাধনার বাড়ি মাদারগঞ্জ উপজেলা বালিজুড়ি ইউনিয়নের সুখনগরী গ্রামে। ঐ গ্রামের নিঃ সন্তান দম্পত্তি খাজু মিয়া ও কুমকুম বেগমের দত্তক নেয়া মেয়ে এই সাধনা। কোন এক রোগের কারনে ছোট থাকতেই তার চুল ও ভ্রু উঠে যায় এবং সেই থেকেই সে মাথায় কৃত্তিম চুল লাগিয়ে নিয়মিত হিজাব ব্যবহার করে। গ্রামে থাকতেই বাল্য বিয়ে হয় জোনাইল গ্রামের জাহিদুল ইসলাম ফরহাদ এর সাথে। বে সরকারী কোম্পানী তে চাকুরী করতো সে। পূর্ণ নামের এক ছেলের জন্ম হয় তার ঘরে। ছোট থেকেই দুষ্ট ও অসৎ চরিত্রের অধিকারী সাধনা বিয়ের পর স্বামীর সাথে বনাবনী হচ্ছিলো না। তার মধ্যেই সালে তার স্বামী ফরহাদ এর অাকস্মিক মৃত্যু হয়। এই মৃত্যু নিয়ে তখন নানান অালোচনা চলে। স্বামীর মৃত্যুর পর তারা স্ব পরিবারে মা বাবার সাথে জামালপুর শহরের বগাবাইদে বাসা ভাড়া নিয়ে বস বাস করেন। এই অবস্থায় তার বেপরোয়া চলাফিরা সবার চোখে লাগে। সে সমাজসেবা অফিসে প্রশিক্ষন নিতে গিয়ে জনৈক কর্মকর্তাকে ফাদে ফেলে তিনি তড়িঘডি করে বদলী নিয়ে চলে যান। এর মধ্যেই টাঙ্গাইলের এক পুলিশ কনস্টেবল এর সাথে পালিয়ে গিয়ে বিয়ে করে। অসৎ চরিত্রের কারনে সেখানেও সংসার টিকেনাই। অাবার ফিরে অাসে বাবার সংসারে। অাবারো বেপরোয়া চলাফেরা ও বিভিন্ন অাসামাজিক কাজে অভিযুক্ত হয়। সম্প্রতি ডিসি অাফিসে পিয়ন পদে চাকুরী করার সুবাদে চাকুরী বানিজ্য সহ ভর্ত্তি বানিজ্যর করার অভিযোগ উঠে। এবং ডিসির ভিডিও কেলেংকারী র দায়ে টক অব দ্যা কান্ট্রি তে পরিনিত হয়। এবং অালোচিত হয় সাধনা নামটি।,0,crime
মেয়ে কে রিমেন্টে নিলে সব বের হয়ে আসবে,0,crime
ক্ষমা সুন্দর দৃষ্টিতে দেখবে আহারে দেশ দেশ আমার শকুনের থাবা তলে সিসিটিভিতে স্পষ্ট সে অপকর্ম করে বলে আমি মানুষিক বিপর্যস্ত আর আমরা মেনে নি ক্ষমা সুন্দর দৃষ্টিতে। নষ্টের কবলে যেতে যেমন আমাদের মিডিয়া উৎসাহিত করে তেমনি তেমনি এই মিডিয়া আবার দামাচাপা দিতে সাহায্য করে।,0,crime
এরা দুইজন যে অপরাধ করেছে সরকারি চাকরি হিসেবে তাতে করে এদের দুইজনকে বাংলাদেশ থেকে বের করে দেওয়া উচিত আপনারা কি বলেন আমাকে কমেন্ট করে জানাবেন,0,crime
মিন্নি জরিত চিল কারন পিচনে হেটে হেটে গিয়েছি যখন ঐ মেয়ের সামনে দিয়ে তকন মেয়ে কিছু বলে নাই!!!!,0,crime
সারের কোনো দুষনাই দুষ সি সি কেমেরার,0,crime
ডিসির রুমে সিসি ক্যামেরা আছে এটা কি ডিসি জানতো না 😌,0,crime
আমি কোখনো কমেটন কোরিনাি এখানে ছেলে আর মেয়ে যেকোযোন আছোলো সোবাই খুনি এটা আমাদের পোদান মোনতি দেখেনা পুলিশ তো তাগমোতন এটা কিবাবে বিচার হবে তারা তো দিনে হাযার হাযার হারাম খায় আর খুনিদের মামু খালু আছে যানিনা তোবে সাছতির আবেদোন যানালাম,0,crime
ক্ষমতা আর জোর দিয়ে আল্লাহ্ পরীক্ষা করেন তাঁর বান্দা কি করবেন বড় আফসোস লাগে তার মত বড়পদে থাকা লোকটির কত থার্ট ক্লাস চরিত্র। আর মেয়েটা ও কি র্নিলজ্জতার পরিচয় দিল আজ কোন আরব দেশে এরকম হলে উভয়েরই গর্দান যেতো সর্বক্ষেত্রে এরকম হচ্ছে এটা তো শুধু একটি ঘটনা এ দেশে ডেঙ্গু মহামারী হবে না তো কোন দেশে হবে আসতাগফিরুল্লাহ্ আল্লাহ্ ক্ষমা করো এই কুলাঙ্গারদের জন্য আমরা র্নিদোষ মানুষগুলোও গজবে পতিত হই।,0,crime
মিন্নিকেও বিচারের আওতায় আনা হোক,0,crime
মানুষ কত ভরো কাফের হলে একজন মানুষকে দিনে দুপুরে দা দিয়ে কুপিয়ে হত্যা করতে পারে এই কাফেরের বাচ্চারা একটু মনে করলোনা ওকে আমরা মেরে আমারা জিন্দা থাকতে পারবে আমার দাবি হাসিনার কাছে এই খুনিদের সকলের ফাঁসি রিফাত শরীফের খুনি এক নাম্বার আসামি জাহান্নামে গেছে দুই নাম্বার আসামি রিফাত ফরাজিকে দিনে দুপুরে জাতীয় সামনে ঐকলেজের সামনে ঝুলিয়ে ফাঁসি দিতে হবে যা দেখে বরগুনার মানুষ সান্ত পায়ে কারন এই দুই সন্ত্রাসী রিফাত শরীফের হত্যা মুল নায়ক নিয়েন বন্ড আর রিফাত ফরাজি,0,crime
মিন্নি জড়িতো,0,crime
এসব প্রসাশকদের বিচার হয়না,0,crime
এটা উনি সরল মনে করেছেন তাই এটা কোনো অপরাধ না,0,crime
তুূদের বাবার টাকা দিয়ে খেলে এই অবইদ্য সরকার পাচঁ ওয়াকত্ত নামাজ পরলে মেরে ফেলে তার বিচার করতে পারিস না লেজাগারে ছেলেরা,0,crime
এই ভিডিওটি কি প্রশাসন দেখে নাই তারা মিননিকে এখনও গেরেপ্তার করিতেছে না কেন না আপনারা এখনও অডার পাননি,0,crime
মিন্নি কে এমন শাজা দেওয়া হকো যে অার কোন নারী যাতে এমন কাজ না করতে পারে,0,crime
রিফাত শরীফ হত্যার সাথে মিন্নি সরাসরি জড়িত এটা আমার বিশ্বাস । তাই আমরা জনগণ মিন্নির ফাঁসি চাই। এই নষ্টা মেয়ে বেঁচে থাকলে ভবিষ্যতে আরো দুর্ঘটনা ঘটতে পারে ।,0,crime
প্রথম কথা এটি নিঃসন্দেহে একটি অসাধু কাজ। কিন্তু একটি সরকারি একটি গুরুত্বপূর্ণ। অফিসের খাসকামরার ভিডিও জিনি বা যারা উর্ধতন কর্মকর্তা দের না দিয়ে সামাজিক যোগাযোগ মাধমে ভাইরাল করলো তাদের তদন্ত করে বিচারের আওতায় আনা অতিব জরুরী।,0,crime
এটাই আমাদের বাংলাদেশের কিছু দিন আগে কটনা টাকে আজ নাটক বানিয়ে পচার হচ্ছে এদের মত কিছু বাজে ছেলেদের জন্য সমাজে নতুন নতুন গুন্ডা জন্ম হয়ে উঠে এই ভিডিও করার কি প্রয়োজন চিল আর কি বুঝাতে চান একনু সময় আছে তুমিও একজন ভালো মানুষ বলে পরিচয় হও,0,crime
এ কয়দিনে তো উচিত ছিল আইন সংগতভাবে তাদের দুজনার বিয়ে পরিয়ে দিয়ে সমাজ থেকে পাপের বিষ কিছুটা রোধ করে দেয়া । আমি বুঝিনা কি আইন বাংলাদেশে ডিসি সাহেবের কুকর্ম লিলা খেলা হলেও এই মেয়েটির জীবন তো সংশয়ে পোরে গেলো এটা ঘৃণিত অপরাধ তার পরেও জীবনের স্বার্থেই ডিসির সাথেই বিয়ে দিয়ে মেয়েটির তো জীবন বাঁচানো আইনের ফরজ নাকি,0,crime
হায় হায় দেশ টা কার হাতে দিমু🙅‍♂️ কি সুনতাছি এই গুলি,0,crime
এই শয়তানদের ফাঁসি চাঁই।,0,crime
হাইরে বাংগালী এতগুলো মানুষ একটু এগিয়ে গেলে কি এমন হত?,0,crime
এদের পিছনে মামু আছে বাংলাদেশে কেউ এদের বিচার করতে পারবেনা 😀হা হা হা😀 হায়রে আল্লাহ কেমন দেশে জন্ম নিলাম,0,crime
আল্লাহ চেষ্টা করলে রিফাত কে বাঁচাতে পারতেন।,0,crime
চোরের ত সব সময় বড় গলা থাকে,0,crime
মিন্নির সামনে মারতে মারতে ওর সামিকে ধোরে নিয়ে যাবার অনেক পরে ঠান্ডা মাথায় মিন্নি গেলো থামাতে মারামারির প্রথমে তো মোনেই হোচ্ছে যে এতে মিন্নি আগে থেকেই জানতো ভালো কিছু ঘোটতে যাচ্ছে !,0,crime
এতো গুলা লোকের সামনে কুপাইছে আর মানুষ সবাই তাকিয়ে দেখছে,0,crime
একজন ডিসিকে সম্মান করে কথা বলা উচিৎ কিন্তু উনাকে ডিসি হিসাবে মানা যায় না।,0,crime
এই রকম নোংরা মেয়ে যদি আমাদের বাংলাদেশে বেচে থাকে তাহলে বাংলাদেশটা নোংরা ভরে যাবে আমাদের দেশে তো আইন কানুন বলে কিছুই সঠিক নয় মানুষ সঠিক বিচার পায় না আমার বাংলাদেশ সরকারের কাছে আবেদন এই মিনি কে ফাঁসি দেওয়া হোক???????,0,crime
হাইরে নিজে আকাম করছে আবার নিজেই তদন্ত করবে। জিনিয়াস তো।,0,crime
ঠিক কতা ভাই ইউটিউবে কিছু পুলা পাইনকে পেদানি দেওয়া উচিত।,0,crime
কষ্ট করে রুজি রুজগার করে ঐটা নিজের খাওয়া আর পরিবারকে দিলে আজ এই অবস্তা হতো না ।দেখো হয়ত তোমাদের পরিবারের কারো প্রানের হাহাকার আজ তোমাদের জন্য কালোরাত হয়ে দাঁড়িয়েছে ।এখনও সময় আছে আল্লাহর দরবারে দুইটা হাত তোলে কান্দ আল্লাহ মাফ করতে পারেন ।,0,crime
দ্রুত তাড়াতাড়ি রায় কার্যকর করতে হবে।মারার পরির্বতে মারতে হবে এটাই চাই।,0,crime
হয়তো তিনি পরে বলবেন এই ভিডিওটির পিছনে বিম্পি জামাত শিবিরের হাত আছে,0,crime
আমার মাথা নষ্ট হয়ে গিয়েছে,0,religion
জে এই ভিডিওটা বানাইছে তার কানের নিচে মারতেচাই আমিন আল্লাহ ওদেরকে বোঝার তোওফিক দাও আমিন,0,religion
মিজানুর রহমান আজহারী 💞💕💕💕,0,religion
ওর মুখে জুতা মারো,0,religion
গাজা খায়,0,religion
তাহেরীর লজ্জা নেই,0,religion
ভাইয়া প্লিজ আমার টা করো প্লিজ প্লিজ 🙏🙏🙏🙏🙏🙏🙏🙏🙏🙏🙏🙏🙏🙏🙏🙏🙏🙏🙏🙏🙏🙏🙏🙏🙏🙏🙏🙏🙏🙏🙏🙏🙏🙏🙏🙏🙏🙏🙏🙏🙏🙏🙏🙏,0,religion
এ নাস্তিকেরে উপর আল্লাহর গজব পডুক। এর ফাসি চাই।,0,religion
এ পিচ্ছী তুই কি কছ,0,religion
দোয়া রইলো আল্লাহ যেন নেক হায়াত দান করেন,0,religion
এনায়েতুল্লাহ আব্বাসী একটা শয়তানের খাড়া জিলকি,0,religion
যেগুলা ডিসলাইক দিসে সেগুলা সবগুলাই দেওয়ান বাগীর সার্পোটার।,0,religion
নাস্তিক দের দেশ থেকে বিতাড়িত করা উচিত ।,0,religion
ভ্রান্তির বেড়াজালে না গিয়ে মুক্ত মনে সত্য কে উপলব্ধি করে জনসমক্ষে প্রচার করার জন্য আপনাকে অশেষ ধন্যবাদ প্রিয় দিভাই।,0,religion
অনেক সুন্দর একটা রোস্ট। আমাদের সিলেটে রোস্ট হয় না। তাই সবাই সমাজকে পরিবর্তন করার নামে ভন্ডামি করে,0,religion
ইসলাম এর বিজয় হবেই ইনসাআল্লাহ্,0,religion
আশ্লেই ইসলাম বিরোধী নাস্তিক ওরা আল্লাহ তালা তাদেরকে হেদায়েত দান করুন,0,religion
ধন্যবাদ ভাইয়া আপনাকে খুব ভাল লাগল আমি আপনাদের সাথে আছি,0,religion
ভাইয়া আসসালামুয়ালাইকুম । একটু সাবধান থাকেন । দিন জামানা ভাল না কিন্তু ।,0,religion
ওরা কাফের কাফের কাফের,0,religion
না না না এটা থিকনা,0,religion
ওদেরকে আমি খুন করবে,0,religion
আসুন একটা গেম খেলি যে যেই টাইমে এই কমেন্ট টি দেখেছেন টাইম টি কমেন্ট এ লিখে যান,0,religion
খুব ভালো লাগলো আপনার কথাগুলো! আজহারী হুজুরের বক্তব্য আমি স্বয়ং নিজে শুনেছি এবং সামনাসামনি! তিনি যতগুলা কথা বলেন কোরআন এবং হাদিসের আলোকে যুক্তি দেখিয়ে কথা বলেন। চরমোনায়ের পীর ডক্টর জাকির নায়েক স্যারের সম্বন্ধে অনেক কটুক্তি উপস্থাপন করেছেন! আমি চাই আপনি চরমোনাই কে ধোলাই করার একটা ভিডিও বের করুন!,0,religion
তাহেরি একজন ভন্ড।।,0,religion
বিসমিল্লাহ মাঃ মিজানূর বলেছেন নবীজি নিরক্ষর ছিলেন এই কথা নিয়া কোন কোন আলেম ফতুয়াদেন মাঃ মিজানূর কাফের বলেন তারা কি যানে না এক মুসলমান আর এক মুসলমান কে কাফের বললে কি হয় তারা কি। কোরান বা হাদিসে পাই নাই মনে হয় তারা ফতুয়া কেতাব পড়েন নাই।,0,religion
চার নাস্তিক কে জুতা পিটা করা হউক,0,religion
লোকটা খারাপ কিছু বলেনি হুজুরটা গিবৎ করছে,0,religion
তাহেরী সঠিক পথে আছে মিজান ভুল পথে আছে,0,religion
দুধ এর কথাটা ছেলেদের কথা চিন্তা করে বের করা হয় নি। কিন্তু দেওয়ান বাগি বাবা বরই দয়ালু হওয়ায় ছেলে দেরও চিকিৎসা করে আসছেন।,0,religion
সোনা খাড়ায়া গেল,0,religion
তাহেরী কে আবশ্যই মানুষ প্রত্যাক্ষান করবেই,0,religion
ভালো লাগলো ভাই,0,religion
পির বেসির ভাগই টাকা ও লুচ্চামি করার পাগল,0,religion
শাহজালাল ইয়ামানী রহমাতুল্লাহ আলাইহির নামে তার গীবত গাওয়া টা ঠিক হয়নি আপনারা কমেন্ট করেছেন আমরা সবাই হয়েছি না আর আপনি তো তাদের সাথে মাথা নিয়ে মাথা ঝাকিয়ে দিচ্ছেন কমেন্ট করতেছেন আগে নিজেকে নিজে নন পরে অন্যের নামে গীবত গান,0,religion
নাওজ বিল্লা আসতাগ ফিরুল্লা,0,religion
পিঠানো দরকার ছিলো,0,religion
বেয়াদব,0,religion
আমি একমত,0,religion
অমানুষ টা,0,religion
ঠিকভাবে জুতা পিটা লে এগুলো ঠিক হবে সালাদের কোন লজ্জা শরম নেই এইসব লোকের কারণে অনেক সহজ সরল মানুষ গুলো এই লাইনে যাচ্ছে আল্লাহ সবাইকে হেদায়েত দান করুক,0,religion
এটা আলেম না সে শিশু তার কি সনত বা দাওরা হাদিস শেষ করনি সে কিবাবে আলেম হয়,0,religion
হাফিজুর রহমান সিদ্দিকি একজন আহলে হক আলেম। আর একটু ভাবা দরকার ছিলো। আর হেলিকাপ্টার সমন্ধে আরেকটু জানা উচিত। কেনো আলেমরা হেলিকাপ্টার ব্যবহার করেন।,0,religion
তোরে যদি পাইতাপবন্ড,0,religion
এই ছেলে বসে মুততে শিখে নাই সেও অন্যের সমালোচনা করে। এই ছেলে শরিয়ত তরিকতের কি জানে কি বুঝে?? যারা এসব বালপাকনা বাচ্চাদের ওয়াজে দাওয়াত দেয় আর যারা এদের ওয়াজ শুনে সবগুলো মুর্খের জাত।,0,religion
আমার দেশে এগুলো কি? কয় বছরের মানুষ তুমি? নাক টিপলে এখনো দুধ বের হবে। ভালো মন্দ কি ভোজ। এগুলো কিয়ামতের আলামত।বাপের বেটা হলে তাহেরীর সামনে যাবি।,0,religion
দেওয়ানবাগির পরিবাররে আমার জুতা করবনা,0,religion
আসসালামু আলাইকুম ভাই ও বন্ধুরা এ বক্তা ভন্ড বক্তা তাদের কারণে বাংলাদেশ অনেক ধরনের সমস্যা সাধারণ মানুষের বিভ্রান্তির কারণ এই আলেম এই বক্তারা তাদের মত যারা আছে একটা না একটা সমস্যা বজায় রাখতে,0,religion
মামুনুল হক হুজুর নাস্তিক দের সাথে তর্কে পারবেন না কারন তারা মুর্খ,0,religion
মাশা আল্লাহ আজান টা হৃদয় ছুয়ে গেছে,0,religion
এই নাস্তিকদের কে নিয়ে আমার মনের মধ্যে যে ক্রোধ তৈরি হলো তা ভাষায় প্রকাশ করতে পারলাম না,0,religion
ঔ সালা এককিক বারে খাটাস,0,religion
মাশাআল্লাহ হুজুর,0,religion
পৃথিবীর অনেক দেশের ছেলে মেয়ে বিখ্যাত গায়িকা নায়িকা খেলোয়ার ইসলামের বানী শুনে কেঊবা আজান শুনে কেউ শুধু হিজাব পড়া নামাজ পড়া দেখে মুসলিম হয়েছে। আমি মনে প্রানে দোয়া করি তারা যেন বাংলাদেশকে ℅ মুসলিম এর দেশ ভেবে এই দেশে যেনো না আসে। যদি আসে তাহলে আমাদের লজ্জার কোনো সীমা থাকবে না।,0,religion
এই ধরনের মাজার পুজারী কিভাবে স্টেজে উঠে বসে?এদের জুতা মেরে বাংলাদেশ থেকে বিদায় করা হউক।,0,religion
দেওয়ানভাগীকে ভরা হইছে😝😝,0,religion
এখানে হাফিজুর রহমান কি ভুল বলছে,0,religion
টাইটেল কি লিখছেন আজহারি হুজুর ভন্ডনা।খুবই মিষ্টিবাসি আর শিক্ষিত মার্জিত মিজানুর রহমান আজহারি।তারমত লোক হয়না💯💯💯 যারা হুজুরকে ভালোবাসেন তারা লাইক দিবেন 🔜,0,religion
হাফিজুর রহমান সিদ্দিকীর কথায় এখন নিজেই ধরা খেয়েছেন ।ডাক্তার জাকির নায়েকের টাই পড়া নিয়ে সমস্যাটা কোথায়??,0,religion
হাজার হাজার আচে এইরকম ভন্ড পির,0,religion
জেদিন তোর পতন হবে বুজবি আল্লা কি করতে পারে নাস্তি কের বাচ্ছা সোন তোরে তো আমার আল্লা আরে মানুষ তো মরার সময় মাটি পায় আর তোর মৃত্যু এমন এহে শকুনে টেনে খাবে,0,religion
তাহারি কুত্তার বাচ্চা মিজানুর রহমান আজাহারির পায়ের কাছেও যেতে পারবে না। থেকে দেখছি খুব ভালো লাগছে ভাই তোমার ভিডিওটা।,0,religion
আল্লাহ এদের কে হেদায়াত করুন,0,religion
আমার পূর্ব পুরুষেরা বাংলায় ইসলামের বানী নিয়ে এসেছিলেন ষ শতাব্দীতে তদনীন্তন কুমিল্লা জেলায়। এখন আর সেই দিন নাই। আমার পূর্ব পুরুষেরা কখনোই কারো কাছে বলেন নাই তাদের আধ্যাত্মিক শক্তির কথা । শেষ আমার দাদা একজন ভাল মাওলানা ছিলেন কিন্তু কখনোই উনি মনে করেন নাই উনি পীর । মুরীদের কথাই আসতে পারে না। আজকের বাংলাদেশে সুন্দর কেরাত পাঠ করে বলে আমি অমূখ জায়গার পীর বা পাগলা বাবা। নিজে নিজে ইসলাম জানুন অনুশীলন করুন আপনি আল্লাহ কে পেয়ে যাবেন। মানুষের ওয়াজ না শুনে কোরআন পড়ুন সহী হাদিস পড়ুন। যেটা রাসুলুললাহ স আমাদের উম্মাকে নির্দেশ দিয়ে গেছেন।,0,religion
মামুনুল হক সাহেবের পাশে টা কুত্তা বসে আসে! এদের কিসের শিক্ষা দিবে! এরা প্রকাশ্য শত্রু ইসলামের। জবাই করা দরকার ধরে ধরে এদের।,0,religion
এগুলা কে ধরে জুতাপেটা করা কাম,0,religion
সম্পুর্ন তাওহিদবাদীদের কথা,0,religion
ঠিক ভল ছেন আমরা সবাই পাসের আছি মিজানুর রহমান আজহারি 👌🌹🌹✋✋✋✋,0,religion
বেশি বেশি টাকা কামানোর একটা সহজ কৌশল হলো মিথ্যা ভিডিও প্রচার করা।,0,religion
কাজী না পাজি,0,religion
এ দেশে দেওয়ানবাগীর মত শয়তান থাকে দেখলেই লজ্জা হয়,0,religion
অনেক দিন অপেক্ষা করে ছিলাম দেওয়ানবাগীর ভরাভরি দেখার জন্য।।,0,religion
এই বেটা মূর্খ বাচ্চা হযরত মা ফাতেমা আজ থেকে বছর আগে মৃত্য বর করেন?? মৃত্য মানুষকে কি করে বিয়ে করেন বেয়াদব?? হযরত মা ফাতেমাকে নিয়ে এই ধরনে কথা বলার সাহস পাইছ কোথায় তর মা আর বাবার পিক দে তারপর দেখ কিভাবে এক্স ভিডিও বানাই। মূর্খের বাচ্চা এগুলো সব এডিট কাটিং করা ভিডিও,0,religion
জুতাপেটা করার পর ও যেই জাহেল মানুষ হয় নি তার সম্পর্কে আর আলোচনা করার মত কিছু নাই আল্লাহ্ এই শয়তান কে হেদায়েত দান করুন,0,religion
নাছতীক,0,religion
তাহেরী টাটকা শয়তান,0,religion
আল্লাহ হেদায়েত দান করুন। আমিন,0,religion
এই শালা এসব কি দেখে না,0,religion
ভাইয়া এগলো কাফের,0,religion
আল্লাহ সবাইকে বুঝার তৌফিক দাও।।সবাই যেন সঠিকটা বুঝতে পারে।।।,0,religion
আমির হামজা হয়তো ভুলে গিয়েছে এটা ডিজিটাল যুগ তার কারণে মিথ্যের আশ্রয় নিচ্ছে এই যুগের একটা কথা সব গুলার প্রমান থাকে এবং এই কথাটার রেকর্ড আছে আপনারা চাইলেই দেখতে পারেন,0,religion
এই চেনেল তোর জন্মের ঠিক আছে,0,religion
যে শালা ওয়াজ করতে আসবে সেই শালাদের অস্ত্র টুপি পাঞ্জাবি খুলে নিতে হবে । সাইনবোড খুলে নিলে ব্যবসা বন্ধ হবে এদের ।,0,religion
এদের কারণে দেশের এই অবস্থা,0,religion
তুই মদারি হলি ইহুদীদের দালাল,0,religion
ওদের কে যবাই করতে হবে। কোটি মানুষের সামনে। আমাদের ভাগ মুসলমান দেশে নাস্থিক আছে।কিন্তু আমরা কিছু করতে পারছি না ম।ছি ছি আমাদের দেশে যুদ্ধ অপরাধীদের বিচার হয়।আদেয় সে দোষ করেছে কী?? কিন্তু নাস্থিক কিছু করতে পারি না।আপছোচ!!,0,religion
এই বেয়াদবদের রাস্তায় পেলে মারার দরকার।,0,religion
কি যুগ এল একজন আলেমকে আরেকজন নাস্তিক দিয়ে অন্ন এক মুসলমান অপমান করাছে ছিঃ ছিঃ আল্লাহ্ লানত পড়ুক এইসব মানুষদের উপর যদি অন্ন ধর্মের সংস্কৃতি আমাদের সমাজে বিদ্বমান তবে এখন বিধর্মী সংস্কৃতি ধর্মের উপর চাপ পেশার করবে ইসলাম ধর্ম সংস্কার করার জন্য উতক্ত করবে এটা কখনো মানা যাবেনা তাহলে ইসলাম বলতে কিছু থাকবে না নাস্তিকদের বয়কট করুন ও সকল মোমিন ভাই অন্তদৃষ্টি সবসময় জাগ্রত রাখবেন।,0,religion
তোর ভক্তদের জুতা মারি,0,religion
হিন্দুরা মুসলমান হলে যা করে থাকে,0,religion
আমাদের সরকার এইসব ভন্ডের নজরদারি কেন করেন না!আর কত দিন চলবে এই ভন্ডামী?,0,religion
মাবুদ এই নাসতিকদের হেদায়েত দান করো,0,religion
ভন্ড তাহেরী গান করে পাক্কা শয়তান,0,religion
চার নাস্তিকের তর্ক শুনে শরীরের রক্ত বেশি গরম হয়ে গেছে 🗡🗡😡😡,0,religion
এই নাস্তিকদের ফাসিঁ চাই,0,religion
এই ভিডিওটা শুধু ভিউজ বাড়ানোর জন্য ছাড়া হয়েছে,0,religion
আল্লামা মামুনুল হক হুজুরকে আল্লাহ হায়াত রিজিক বাড়িয়ে দাও আমিন,0,religion
মুরগী কবির,0,religion
অনেকদিন পরে আপনার পোষ্টে কমেন্ট করছি। একটা কাজের কাজ করছেন ভাই। এই লোক যে কত খারাপ সেটা আমরা জানি। আগে একটা কন্ট্রোভার্সিয়াল বিষযে না জেনে কথা বলার জন্য আপনাকে আনসাবসক্রাইব করে দিছিলাম তবে আজকের ভিডিওর পরে আবার সাবসক্রাইব করতেছি।,0,religion
তোর মাতা তোরে জুতা মারা দরকার তখন,0,religion
এই ভিডিও দেখে কেন জানি একটা প্রশ্ন আসছে যেসব কথিত নাস্তিক দের সামান্য এর কারনেই তাদের হত্যা করা হয় কিন্তু এই দেওয়ানবাগি এখনো বেচে আছে কেম্নে?? আর কেও প্রতিবাদ ও করে না কেন ?? এদের দিতেছেই বা কে ???,0,religion
জানোয়া,0,religion
বাংলার মাটির মানুষ মিজানুর রহমান,0,religion
আপনার মাথায় টুপি কোথায়,0,religion
চালিয়ে যান ভাই দোয়া রইল,0,religion
যারা ডিসলাইক দিছে তারা দেওয়ানবাগী ভক্ত।😂,0,religion
তাহলে হজ করতে গেলে মাথা নেরা করে কেনো,0,religion
এই সব ভুল কথা বলছো কেন,0,religion
আমিত এখানে অপমানের কিছুই দেখলাম না,0,religion
সয়তান সব গুলা,0,religion
আমি সবিনেয় জানতে চাই জনাব শাহরিয়ার কবির আপনার মৃত্যুর পর কোন রীতিতে শেষ কৃত্য সম্পাদিত হবে,0,religion
এ হলো আর এক বাল ফালা।পুরা ওয়াজে শুধু গিবত করলো ইসলাম সম্পর্কে কিছুই কইলো না,0,religion
এই যমানার ফেরাউন দেওয়ানবাগী,0,religion
কে কে মিজানুর রহমানের পাশে,0,religion
এরা খাস ভন্ড,0,religion
বাবুনগরী নাকি সব সুর সুর করে বলে দিয়েছে এই জানুয়ার মুরগী কবির কিভাবে ডাহা মিথ্যা কথা বলে যাচ্ছে,0,religion
থু থু কতাকার হালারপুয়া যুক্তি শিখাইতে আইছে !!,0,religion
তোদের জন্মে সমস্যা আছে,0,religion
আপনাকে অনেক ধন্যবাদ এমন ভিডও তৈরী করার জন্য,0,religion
মাশাল্লাহ হক কথা বললেন,0,religion
এই চার নাস্তিকের গালে জুতা মার তালে তালে,0,religion
আমির হামজা একজন ভালো হুজুর,0,religion
এ যে নো একটা বাঘকে তিন চারটা শকুনের থাবা। কিন্তু কাজ হয়নি বাঘ বাঘ ই থাকে।আর শকুন খুজে গরু মরা,0,religion
জুতা মার সুয়ররে মাজার পুজারি,0,religion
রাইট কথা বলেন,0,religion
≈,0,religion
ওর চুল দেখলেই মেজাজ খারাপ লাগে তাহেরির,0,religion
হুজুরটা হচ্ছে এক নম্বর ভন্ড,0,religion
আসসালামু আলাইকুম তাহসিন ভাই আল্লাহর আকার বলাটা ভুল হবে কিন্তু নিঃসন্দেহে আল্লাহর সুরাত আছে। কারণ ওইটাকেই বলে আসমা আস সিফাত। অর্থাৎ আল্লাহর হাত পা চেহারা সব কিছুই আছে। তবে তা আল্লাহর শান মোতাবেক। এইটার উপর ঈমান না আনলে আমরা কাফেরে রুপান্তরিত হয়ে যাবো। প্রমাণ চাইলে প্রমাণ ও দিতে পারবো সয়ং কুরআন থেকেই ইন শাহ্ আল্লাহ। আল্লাহ আমাদের সকলকেই বুঝার তৌফিক দিন।,0,religion
এখানে কয়েকজন ভণ্ড আছে ঠিক কিন্তু অধিকাংশই মুহাক্কিক আলেম। আপনারা সবাই তাদের কয়েকটা মাহফিল দেখবেন তারপর মন্তব্য করবেন। বিশেষ করে খালেদ সাইফুল্লাহ আইয়ুবি জুবায়ের আহমদ আনসারির নাম এখানে একেবারেই অপ্রাসাঙ্গিক।,0,religion
আব্বাসী হুজুরে ঠিক আছে তো? সে তো কাফের ছাড়া কাউকে চোখে দেখে না সে তো বরগুনা জেলার পাথরঘাটা থানায় মাহফিল করতে আসলেই ঝড় উঠে আর একটা কথা হলো সে তো আওলাদে রাসূল ভোলায় বোরহানউদ্দিন এ যে নবী সঃ এর বিরুদ্ধে যে কুলাঙ্গার কটুক্তি করছে তার বিরুদ্ধে সে কোনো আন্দোলন করছে মনে হয় না না নামলো মাঠে আর না করলো মিডিয়ায় কোনো প্রতিবাদ হুজুর কিভাবে আসেকে রাসূল দাবি করতে পারে! আমরা যারা আশেকে রাসূল দাবি করি কিন্তু আমরা যারা প্রতিবাদ করতে পারলাম না আমরা তো ভন্ড আশেক রাসূল এর তালিকায় আছি বার বার প্রশাসনের ছত্রছায়ায় হিন্দুত্ব বাদীরা আমাদের উপর আক্রমন করছে কখনও মসজিদের উপর কখনও মুসলিমের উপর কখনও আমাদের প্রাণের চেয়ে প্রিও মুহাম্মদ সা এর উপর কিন্তু কখনই এর বিচার হয়নি এর বিচার আর কোনো দিন হবেও না নারায়ণ গঞ্জের শ্যামল কান্তি নাসির নগরের রশরাজ রংপুরের টিটু রায় বিপ্লব চন্দ্র শুভ একজনের কি বিচার হয়েছে নবী স এর উপর আক্রমন কি থেমেছে কিছুই হইনি চিন্তা করুন ভাই মালাউনের বাচ্চারা কাকে গালি দিচ্ছে কাকে নিয়ে কটূক্তি করছে আমাদের নবী স কে আল্লাহর রাসূল স কে এই মানুষটি তো আমার আপনার জন্য রাতের পর রাত জেগে আল্লাহর কাছে কেদেছে আমাদের আখিরাতের মুক্তির জন্য রাতের পর রাত সালাতে দাড়িয়ে থেকেছেন আল্লাহর কাছে ফরিয়াদ করেছেন কেবল আমাদের কাছে তাওহীদের বাণী পৌঁছানোর জন্য নিজের বাড়ি ঘর ছেড়ে মদিনাতে হিজরত করেছেন মাসের পর মাস অভুক্ত থেকেছেন তায়েফে পাথরের আঘাতে জর্জরিত হয়েছেন উহুদের ময়দানে নিজের রক্ত জড়িয়েছেন হাসরের ময়দানে যেদিন বাবা ছেলেকে চিনবে না মা সন্তানকে চিনবে না যখন সবার মুখে থাকবে ইয়া নাফসি নাফসি তখন আমাদের নবী স বলবেন ইয়া উম্মাতি ইয়া উম্মাতি বিচারের সেই দিনও আমাদের নিয়ে দুশ্চিন্তা করবেন আমাদের জন্য আল্লাহর ইচ্ছায় শাফাআত করবেন আমাদের জন্য হাউজে কাওসার অপেক্ষা করবেন তিনি আমাদের প্রিও নবী মুহাম্মদ রাসূলুল্লাহ সাল্লাল্লাহু আলাইহি ওয়াসাল্লাম। আল্লাহর কসম আল্লাহর ইজ্জতের কসম আসমান ও জমিনের মালিকের কসম করে বলছি আমাদের জীবন বৃথা যদি না আমরা রাসূল সাল্লাল্লাহু আলাইহি ওয়াসাল্লাম এর সম্মানের হেফাজত না করতে পারি।,0,religion
স্যার আপনাকে শোত শতো সালাম জানায় আপনির ওয়াজ শুনলে মন ভরে জায় আমীন ♥♥♥,0,religion
কি হিংসা হয়,0,religion
বাবু বাংলাদেশে অনেক মানুষ আছে তাহেরিকে নিয়ে সমালোচনা করার তোমার বয়স হয় না তুমার যদি আদব থাকতো তুমি মুরুব্বিদের সামনে উঁচা জায়গায় বসলা কেমনে??? তোমার এখন পরালিখা করার বয়স ওয়াজ করার বয়স না আমি ব্যক্তিগত ভাবে তাহেরিকে পছন্দ করি না কিন্তু তোমার অবস্থান কথাবার্তা আর তোমার বয়স দেখে তোমাকে আমার বেয়াদপ মনে হইলো,0,religion
এই সব ভন্ড পীরদেরকে জুতা পিটা করুন,0,religion
আমার ক্ষমতা থাকলে ওই শয়তানকে সবার সামনে পাথর নিক্ষেপ করে মারতাম আর যে কি কি করতাম।।।। আমাদের প্রধানমন্ত্রী ওই শয়তানকে কিছু বলেন না কেন?,0,religion
★এই গুলার কথা শুনে আর সয্য করতে পারতেছি না আমার হাত চুল্কাতেছে। মন চাইতেছে কসাই দুইটা বসাই দেই দুই গালে।,0,religion
মিজানুর রহমান একজন ঈমানদার মানুষ মনে হয় আমার মতে আমার বাড়ি ভারতের পশ্চিমবঙে আমি প্রতি নিয়ত তার জলসা শুনি ইউটুবে,0,religion
আপনি মূর্খতা করেছেন মিজানুর রহমান কে গালিগালাজ করে ।নিজের অবস্থান খেয়াল করুন ।,0,religion
তোমাদের ধর্মীয় গোঁড়ামির জন্য তোমার সারা বিশ্বে পিছিয়ে পড়া দেশ হয়ে থাকবে। প্রকৃত সত্য আগে জানুন তারপর না হয় গালাগালি করবেন নাস্তিকদের।,0,religion
তিন কুত্তার জন্য একটা বাঘ,0,religion
মদনা।ঘরে মদনা।তাহেরী।হুজুর তুর।বাপের চাইতে সিনিয়র,0,religion
সবাই যদি ভন্ড হয় তাহলে আসলটা কেটা একটু বলবেন মওলানা সাহেব,0,religion
সবচেয়ে দুঃখের বিষয় এই যে এইসব কিছু ভন্ড লোকদের কারণেই নাস্তিক কাফেররা ইসলাম ধর্মকে নিয়ে ঠাট্টা মসকরা করে 😭😭,0,religion
আওয়ামীলিগ কে গালি দিবনা অনুরোধ করি এরকম নাস্তিক যেন দলে না থাকে,0,religion
আল্লাহ আপনাকে তার দিনের জন্য কবুল করুক।,0,religion
গীবত করার জন্য যোগ্যতা লাগে। এই শয়তান পিচ্চির তাও নেই,0,religion
মাশআল্লাহ বাবুটার হাঁসিটা খুব সুন্দর,0,religion
আমি মনে করি এদের সাথে কথা বলা উচিৎ না,0,religion
শুধুমাত্র কয়েকটা পাওয়ার উদ্দেশ্যে এমন টাইটেল কিভাবে দিতে পারলেন? তাহেরি বা দেওয়ানবাগী কি আপনার চাইতেও বড় ভন্ড? আমি মনে করি তাদের চাইতেও বড় ভন্ড আপনি। যদি ভাল মানুষ হতেন তাহলে অন্তত ভিডিওটিতে সম্মানজনক টাইটেল ব্যাবহার করতেন।,0,religion
এখন ত বুজবিনা মরলে বুজবি,0,religion
ভাইয়া রানার গানটা চাইইইই,0,religion
মাজার পুজারিরা পাগল হয়ে গেছে তাদের সারতে আঘাত লাগলো 😹😹,0,religion
ওয়াও ভাই আপনারা ভিডিওটা খুব সুন্দর করে সাজিয়েছেন তাই আপনাকে ভিডিওটার সাজানোর জন্য,0,religion
আমি দেওয়ানবাগীর ফাসি চাই আইনী ভাবে,0,religion
ভাই এই ভন্ড পীরদের মুখোশ খুলে দিন,0,religion
চার কুকুর,0,religion
মিজানুর রহমান আজহারি ভন্ড তাহেরিকে কিভাবে ধুয়ে দেবেন? সেতো নিজেই একজন ভন্ড,0,religion
এরা ভাল,0,religion
এই বক্তা হাফেজ ও আলেম।,0,religion
আপনি অনেক ভন্ডদের উম্মোচন করেছেন কিন্তু তাদের সাথে আপনি কিছু ভালো মানুষ কে ও চালিয়ে দিয়েছেন। যেমনঃ চরমোনাই পীর সাহেবের ভিডিওটি হাফিজুর রহমান এর আর ওয়াজের মধ্যে কিছু অকাট্য কথা বলে এসব স্বাভাবিক কিন্তু আপনাকে ধন্যবাদ আপনার ভিডিও গুলি যথার্থ পুরষ্কারপ্রাপ্তির কাজ।,0,religion
ইসলামের মডেল মক্কা মদিনা না বরং কুরআন ও হাদিস।,0,religion
শাহরিয়া বলছে তার ছেলেরা আর তারা ছেলেরাই তার স্ত্রী র উপর পশুর নজর দিয়েছে। আর হেফাজত কোরান পুরালে তাহলে তারা কি করছে কোরান কে??,0,religion
যেই বয়সে ইসলাম বুঝার কথা সেই বয়সে ইসলাম বুঝাতে আসছে তবে ভাই তুমি আগে ইসলাম ভালো করে বুঝতে চেষ্টা করো আরো ভালো হবে তুমি তুমার পড়া শুনা শেষ করো মানুষকে বুঝানোর জন্য সামনে আরো অনেক সময় পাবে,0,religion
সবচেয়ে সহি হাদীস বুখারী হাদিস।,0,religion
তোরা কে জাহানাম ডাকে,0,religion
আমাদের ব্রাহ্মণবাড়িয়ার বদনাম খুব বলে যাচ্ছে এটা কি ঠিক,0,religion
ভন্ড তো তারা যারা মানুষের ভাল দেখলে নিজের চুলকায় । তাহেরীকে একেবারে ভন্ড বলা যাবে না ।,0,religion
ভাই অনেক দিন পরে ভালো বিনোদন পেলাম তাহেরি কাজ থেকে,0,religion
ইফতারের পরে রোস্ট ভালই জমবে ভাই তাহসিন 😊😊😊😊😊,0,religion
এসব ফাজিলের দল,0,religion
এ মুরগি চোরকে আমি যদি পাই তাহলে জুতা দিয়ে পিটাইব,0,religion
কোথায় কায়েদে আযম কোথায় বদহজম।আমির হামজা হুজুর একজন এর কোরআন গবেষক মুফতি।তার সাথে একটা ভন্ড ধর্মব্যবসায়ী মাজারপূজারীর তুলনা করাও তো অন্যায়।তাহেরির মত ভন্ডদের পিটিয়ে মাটিতে গেড়ে ফেলা উচিত।,0,religion
ভন্ড।।।সবাইকে ঈদ মুবারাক,0,religion
আল্লাহ সবাইকে এদের থেকে হেফাযত করুন এবং সবাইকে এগুলো বুঝার তফিক দান করুন ও হেদায়েত দান করুন।আমিন।,0,religion
আল্লাহ এদের বিচার করুন।,0,religion
বাল হচে,0,religion
আপনার নাম বলা ঠিক হয়নি মুফতি নোমান ক্বাসিমিকে বলছেন ওলিপুরি।,0,religion
তোমারা যে দেওয়ানবাগী হুজুর এর বিরুদ্ধে যারা প্রচার করছ আল্লাহ্ তোমাদের হেদায়েত করুক তোমরা মুনাফেকের মত কাজ করিতেছ ?,0,religion
মুরগী চুর কবির কে জুতা খায়ান হক,0,religion
কিরে আপু তর কি মা বাব নাই তুই এসব কথা বলতেছেত,0,religion
আজকের ভিডিও তে আগুনটা বেস্ট লাগতেছে👌👌👌👌 আর ভিডিও টি সেরা। এই ভন্দ্রে জুতা মারা উচিত,0,religion
বছর আগেও একজন দেওয়ানবাগী এসেছিলো। এই আধুনিক যুগে যদি দেওয়ানবাগীর লক্ষ লক্ষ অনুসারী থাকতে পারে তাহলে চিন্তা করুন বছর আগে মানুষের বিস্বাস কেমন ছিল। তখন যদি কেউ একটা মোবাইল বানাতে পারতো তবে তাকেতো মানুষ সৃষ্টিকর্তা ভাবতো।,0,religion
আপনারা বুঝেন না আল্লাহ শয়তানকেও তো একটা কাজ দিছে যদি শয়তান শয়তানি না করে তাহলে কি চাকরি থাকবো?,0,religion
বাংলাদেশ আওয়ামী এ নাস্তিক এর জায়গা নেই,0,religion
তুকে কিছু বলার ভাষা নেই এটা দেখলে সয়তান ও ভয়পাবে,0,religion
তোর বাপে ভন্ড,0,religion
বাজে কমেন্ট করার জন্য আমাকে খমাকরেদাও,0,religion
এই সব বনড হজুরদের জুতা পেটা দরকার। যারা মিজানুর রহমান আজহারির ভুল। ধরে,0,religion
বন্ডা বাচ্ছা তাহেরী সিলেট জুদি ওয়াজে দেকি তরে জুতা পিটা দিমো,0,religion
এই সয়তান তরে ওয়াজ থেলে গারে দরে বের করে দেওয়া উচিত ছিল মাজার জিয়ারত কে ভালো লাগেনা তর তোদের মাজে তর মত মোল্লা দের জন্য এমন হাল দেসে সয়তান,0,religion
এতো ইচড়ে পাকা !!,0,religion
এইসববন্ড পীরদের জুতারমালা গলায়দিয়া সারাদেশেগুরানো উছিত,0,religion
একনও সময় আছে নাসতিকতা ছেড়ে দে না হলে আৱ সময় হবে না,0,religion
এরা সবাই হলো সুফির দলের মানুষ আর যারা এর সাথে সামিল সব তারা ভন্ড আমি সৌদি আরব মাওলানাদের দেখিয়ে ছিলাম তারা বলেন এরা সবাই সুফি আর এদের থেকে দুরে থাক তে আপনি যদি এদের সমার্থ করেন আপনি ও এদের আনতোর ভুক্ত হয়ে যাবেন তাই এদের নাগালের বাইরে থাকতে হবে সুফিদের মানা যাবে না বলতে হবে আসতাকফীরূললাহ মুসলমানদের জিকের হলো কুরআন পডা পোরথম এর পর সুবহানাআললাহ আলহামদুলিলাহ আল্লাহুআকবার লাইলাহাইললাহ মুহামমাদুর রাসুলুললাহ পড়তে হবে ঠান্ডা মাথায় চুপে চুপে কারো ডিষটাভ করা যাবে না এটা হলো ইসলাম ধর্ম,0,religion
এই শালা বাটপার,0,religion
আমাদের সজাগ থাকা সবতেকে বেশি দরকার,0,religion
নাচতিক বেয়াদব,0,religion
ভাই আপনাকে অনেক অনেক ধন্যবাদ এমন ভন্ডের পরিচয় তূলে ধরার জন্য।,0,religion
এই চারটা নাস্তিক । জুতা ছেঁড়া স্যান্ডেল দিয়ে পাটানো উচিত ।,0,religion
তুই একটা ভন্ড ?,0,religion
এইসব হারাহিদের কারনেই আজ ইসলামের সমস্যা এদের কে জুটা পেটা করে ফাহ ফিল থেকে ভের করে দাই।।।।,0,religion
তাহেরি তিন বেলা গাঞ্জা খা,0,religion
যারা অন্যর দোষ খুঁছে বেরায় তারা শয়তার আর ভন্ড আপনি ওনার ভালো দিক তুলে ধরেন খারাপ দিক না,0,religion
দেওআন বাগ থেকে বড় অপরাধী তার ভ্ত্তরা যারা এই কথা গুলা বিশ্বাস করে,0,religion
আপনারা যারা শিশু বক্তা বলেন যেনে তার পরে কথা বলবেন এনি মাওলানা সেশ করে এখন উচ্চ ভালো মানের লেখা পরা জন্য শুরু করতেছেন,0,religion
আমির হামজা একজ ভালো বকতা তাহেরি বন্ট,0,religion
হুজুর হক কথা চালিয়ে জান আপনার সাহসি বক্তার দোকার হুজুর আপনি এগিয়ে আমরা আছি আপনার সাথে,0,religion
ইমান চুরের দল সরব এক সাতে আবুজাহে ছেলেরা সাদারন মানুসে ইমান চুরি করছ তরা,0,religion
হালার ভন্ড কয় কি?,0,religion
ভালো মন্দ এক জায়গায় করে খিচুরি পাকাইছেন।চরমেনাইয়ে বিরোধিতা করে লাভ নাই তওবা করুন।,0,religion
দুখখে আর কি বলবো এগুলা হাস্যকর,0,religion
সুন্দর উপস্থাপন,0,religion
এরা জাহান্নামী 😡😡😡,0,religion
বাচ্চা পোলাপাইন সব টাকা কামানোর ধান্দা যত সব,0,religion
তাহেরি তুর কয়দিনের ছোটরে একটু জানাবি বিয়াদবির একটা সিমা আছে শিশু,0,religion
কাইফা হালুম,0,religion
হাতের আংগুল জেমন সমান না প্রিথিবীতে সব মানুষ ও সমান না জার কম্য জেমন তার ফল তেমনি পাবে হুজুরেরা কি বলেছে তুমি গাজা খাও মাজারে সেজদা কর এগুলি করি আমাদের মতই সাধারন জনগন আমি এই কথাই ভলতে চাই জে কিছু কিছু ভন্ড দের কারনে সবাইকে বলা ঠিক না কারন আল্লাহর অলিরা কখনই বলে না তুমরা খারাপ পথে চল,0,religion
রাত টা বাজে এইসময় কেন,0,religion
এরা চার নাসতিক,0,religion
ধন্যবাদ ভাই এই কুকুরের বাচ্চাকে নিয়ে রোস্ট করার জন্য। লাভ ইউ।,0,religion
ভাই আমি দেওনবাগির দরগায় হামলা করবো আমার সাথে এক মত থাকলে লাইক দিন,0,religion
এই নাস্তিকদের কি বলবো ভাষায় প্রকাশ করতে পারছি না এই নাস্তিকদের দুনিয়াতেই আল্লাহর কাছে শাস্তি কামনা করছি,0,religion
এই সব এর জন্য বাংলাদেশ রা নাস্তিক হচ্চে। কি না হয় বাংলাদেশ এ,0,religion
এর ওয়াজ বয়কট করুন সবাই ফেতনা সৃষ্টি করে আর বড় হক্কানী আলেমদের কাফের ফতুয়া দেয়।,0,religion
মেডাম আপনি কি দেওয়ান বাগিকে চিনেন না তাহিরী তো আর তাদের মত কফুরী করে না।? বুলভা্র্ন্তী বলে নিজের ইমানকে নষ্ট কেনো করেন।,0,religion
মিজানুর রহমান হুজুর সত্যি ভালো একজন আলেম কিন্তু সে তো মাঝে মাঝে নবী স এর মিলাদ কে মানে না সে একটু হাদিস ভালো করে পরুক কারণ বেশি ভালো বলে দেখে সে বারবার বুল করনে,0,religion
তোদের মত বক্তাকে জুতা পিঠা দিতে হবে ।করণ ওহাবীরা কাফেরদের চেয়ে খারাপ। তোদের ক্ষমতা থাকলে প্রমাণ করে যা?,0,religion
উনি কোন বক্তা নাকি তারে জুতা দিয়া পিডা,0,religion
ভাই মুসলমানের আবার আগের জনমে মানে কি,0,religion
এক ভন্ড আরেক ভন্ডের কথা বলে,0,religion
এরা তো নাস্তিক না নাস্তিক তারা যারা কোন ধর্মই মানে না এরাতো শুধু ইসলামকে অবমাননা করে এরা ইসলামের শত্রু,0,religion
বইসা যান বলা অপরাধ না কিন্তু তুমি যে ভাবে বলেছো তাই মানুষে তোমারে নিয়া মজা করে।জিকির আল্লাহ তোমারে বলে নাই তোমার মত করে করতে তুমি যেই ব্যাখা দিছ তা ভুল তুই তাহেরি হইলি বর্তমান যামানার সবচেয়ে বড় ফেতনাবাজ দাজ্জাল।,0,religion
ও মাওলানা তো ডিজিটাল মাওলানা ।। ভয়ঙ্কর মাওলানা ।। ওর তো জেকের । ‌তাতে আবার গানের মতো টাকা দিচ্ছে সবাই । জেকের আবার নাচে কি??,0,religion
মানতে হবে তাহেরি একটা মজার লোক। মানুষকে হাসানো কিন্তুু এতো সোজা না,0,religion
নাউযুবিল্লাহ ঈদ মুবারাক,0,religion
এগিয়ে জাও ভাইয়েরা আরো এগিয়ে জাও,0,religion
কম দামী তাহসিননেশন😂😂😂😂😂 সস্তা তাহসিনেশন😂😂😂😂 বলদ! পুড়াই কপি কপি😂😂,0,religion
দয়াল বাবা কলা খাবা গাছ লাগাইয়া খাও পরের কলা দেখিয়া তুমি মিট মিঠিয়া চাও বাবারে,0,religion
হেড়ে পেলে বিতরে বাঁশ ঢুকিয়ে দেব,0,religion
কোনো কথা না সামনে পাইলে খালি জুতা পিটা করা,0,religion
সঠিক শিরোনাম।নাস্তিক ওরা,0,religion
এরা কেও মুসলিম না ইসলাম শান্তির ধর্ম। কারো মনে কষ্ট দেওয়ার আইন নেই ইসলামে যার যার ধর্ম সেই সেই পালন করবে।কারো বিরুদ্ধে গীবত করা কোন ধর্মে লিখা আছে এক জনের অনুপস্থিতিতে কথা বলা গীবত। যাই হোক কারো মনে কষ্ট দিলে মাফ করে দিয়েন।,0,religion
নাস্তিকদের জোর সব সময় বেশি থাকে কিন্তু তা চিরস্থায়ী না,0,religion
নাস্তিকেরা ইসলামের শত্রু না মিত্রু?,0,religion
তুই নিজে বড় বাটপার,0,religion
তাহেরি মানেই সেরা বিনোদন,0,religion
ভারতে রাম রহিম এর বিচার হতে পারে অথচ মুসলমানদের দেশে এই সব ভেজাল কুকুর বিড়াল অরিজিনাল কুকুর বিড়াল এর চেয়ে ভালো কে কিভাবে বাচিয়ে রাখে এদের বিচার আমি নিশ্চিত শেখ হাসিনা খালেদা সবাই এর মুরিদ 🤬🤬😡😡😡,0,religion
খুব খারাপ লাগে এসব দেখলে আর সত্যি বললে নাস্তিক খেতাব দেবে আল্লাহ্‌ সেইসব মুসলিম ভাইদের হেদায়াত দিক যারা এইসব পিরদের পিছে ছোটে আর মিথ্যাবলা হুজুরদের বিরুদ্ধচারন নয় দমনে কাজ করছি ভাই আর তার পাশে থাকা বন্ধুদের অনেক ধন্যবাদ টি বানাবার জন্য,0,religion
আজানদিতে কি হাত লাড়ায়,0,religion
ভালো আপনার সব গুলা ভিডিও অনেক কিছু বুজার আছে,0,religion
বাংলাদেশের হাজার হাজার মাজার আছে যেকানে গাঁজা খাওয়া হয় 😡😡,0,religion
শুকরিয়া আপনাকে এসব ভন্ডদের রহস্য প্রকাশ করাই জন্য,0,religion
জুতা মারার দরকার তরে,0,religion
তোরা নাস্তিক এর দল তোদের লাখো কুটি জুতার বাড়ি জানোয়ার গুলি আল্লাহ তোদের কোনো দিন ক্ষমা করবে না,0,religion
অাইবার অালী হো,0,religion
নাস্তিক মুক্ত বাংলাদেশ চাই!,0,religion
আরে ভন্ড তাহেরি ডাক্তার যদি সবকরে তাহলে মুত্যুর সময় বাঁচাতে পারেনা কেনো ডাক্তার কেবল মাত্র উচিলা আর কিছু নয়,0,religion
নাউজুবিলা থু থু থু নাউজুবিলা ।।,0,religion
তাহেরী সাহেবের তো কথাই হয় না,0,religion
কোরবানির গরুর মত পোশাক কেন।,0,religion
বাংলা দেশের মানুষ এই সব ভন্ড প্রতারক নাস্তিক গুলাকে দেখতে পায়না আর ভালো ভালো আল্লাহওলা আলেমদের দেখতে পায় যেমন দেলোয়ার হোসেন সাঈদী মিজানুর রহমান আজহারী আমির হামজা এনাদের পেছনে লাগছে তাই আল্লাহ এনাদের সম্মান আরো অনেক বারিয়ে দিচ্ছে আর ওইসব নাস্তিক গুলো মরার পর ওদের জানাজা না পরে মাটিতে পুঁতে ফেলা দরকার ওদের জন্য একটা আলাদা কবরস্থান করতে হবে যার নাম হবে একদম সত্য এই সব কবরবাসী গুলো নিশ্চিত জাহান্নামী।,0,religion
মরলে পরে বুজবি,0,religion
কসম করে চোরে তুইতো বৌ চোর অন্নের বৌ চুরি করে আইনছিস হাফিজুর রহমান চোর,0,religion
সর্বনাশ,0,religion
শুধু কিচ্ছা কাহিনী কুরআন ও হাদীসের কোন কথা নাই পাগল।,0,religion
ধুরো বাল মিনিট দেখচি এর মধ্যে টা এড্ড ডান😑 আরো কয়টা আসবে দেওয়ানমাগি যানে আবার পড়েন।😑,0,religion
তাহেরি তুমি একমাত্র ভন্ড পীর,0,religion
তাহেরির গান শুনে কে জারা শুনে তারাও তাহেরির মত পাগল ছাগল,0,religion
এ রকম ভন্ডাম‌ি আর কত কাল চলব‌ে? আমাদের বি‌বেক কি কখনও যাগ্রত হ‌বেনা? এই ভন্ড দেয়ান বা‌গি‌তো নি‌জে‌কে রাসুল দা‌বি কর‌তে‌ছে তাহ‌লে কেয়াম‌তের পূ‌র্বে জন মিথ্যুক এর ম‌দ্যে জন তো হল তা হ‌লে কি কিয়ামত খুব নিক‌টে? আসুন আমরা সবাই এর তীব্র প্র‌তিবাদ গ‌ড়ে তু‌লি!! এটা‌কে মে‌রে ফেলা ফরয হ‌য়ে‌গে‌ছে!!!!!!,0,religion
গাধা কবরে থাকা ব্যাক্তির কাছে নয় উছিলা নেওয়া হয়!!,0,religion
কে??এরা কারা??,0,religion
এখানে।সবাই।পাগল। ভাই।আপনাকে।অনেক।ধন্যবাদ এই।ভিডিওটা।ভানা।বার।জন্য,0,religion
পড়াশুনা আরো কর সময় আছে বলদ,0,religion
ওরে পাইলে হত্যা করমু। কে কে আমার সাথে একমত??,0,religion
এই ভন্ড দের পায়ের নিচে ফেলে শেষ করে দেওয়া অচিত,0,religion
মিজানুর রহমান আজহারী বাই খুব সুন্দর ওয়াজ করে সালা তাহিরি বন্ড,0,religion
মাশাআল্লাহ কন্ঠ নাকি বাশির সুর,0,religion
হুজুরের ওয়াজকে আল্লাহ কুবুল করুন আমীন,0,religion
ভালো একটা কাজ করেছো এরকম ভিডিও বানানোর জন্য তোমাদেরকে অনেক অনেক ভালো লাগলো,0,religion
আল্লাহ তাকে নেক হায়াত দান করুন,0,religion
ভন্ড বেয়াদব।,0,religion
ভালোকিছু তুলে ধরার জন্য আপনাকে অনেক অনেক ধন্যবাদ। আশাকরি আগামীতে আরো ভালো কিছু পাবো।,0,religion
দাঁতের বয়স হয় নাই তার আবার ওয়াজ করার সখ হয়েছে।,0,religion
চার জন শুধু জন নাস্তিক হলেও একজন মামুনুল হকও যথেষ্ট ।,0,religion
এইটা ক জিকির নাকি বাবার নাম বাবার নামে কি জিকির হয় নাকি আল্লাহর নামে জিকির,0,religion
মূল্যবান কথা বলার জন্য আপনাকে ধন্যবাদ এরকম ভন্ড তাহেরীর মত যারা আছে তাদের বিরুদ্ধে রুখে দাঁড়ানো প্রতিটা মুসলমানের দায়িত্ব না হলে এদের ভন্ডামি বেড়ে যাবে,0,religion
জাকির নায়েকের সামনে কত হাজার হাজার ধর্ম বিরুধী বসে থাকে কথা বলার যোগ্যতাও নাই আর এই চারজন হাস্যকর মজার ব্যাপার হল এই মহিলা মুরগী কার বাড়িতে পোষে??,0,religion
আমির হামজা সত্যের পথে তাহেরি অর্ধেক ভন্ড,0,religion
আব্বাসি ভন্ড মিথ্যা বাদী বিদাতি মাজার পুজারি। কখন কাকে কি বলে সে নিজে ও জানে না।,0,religion
পাশে আছি সবসময়।,0,religion
এ ব্যাটা তো ভন্ড,0,religion
মেয়াদোত্তীর্ণ গাঁজা ভাই😎😎😎😎,0,religion
বর নাস্তিক,0,religion
এরা টাটকা শয়তান,0,religion
অরে মাইরালা,0,religion
সব নাস্তিক লন্ডনে এ গিয়ে পলায়,0,religion
আর যেগুলা জিকির করে এগুলো তো আচ্ছা ছাগল আর ।তাহিরিরে যদি কাছে পাইতাম তাহলে ওর পিঠের চামড়া উঠাইয়া লাইতাম ও জিকির করে না ফাইজলামি করে ভন্ড ওরে জুতা দিয়ে পিটানো উচিত,0,religion
শাহ জালাল সাহেবের মাজার আমার থেকে টার রিস্কা ভাড়ার দূরে এই দরগায় ইকরামের কাপর যেটা দিয়ে হাজীরা হজ করতে যান পরিধান করে উরুস নামের গাঁজার আসরে বসে একদিকে নামাজ হয় আর তার পাশেই গান বাজনা বাজানো হয়।,0,religion
ভন্ডামির সিমা ছারিয়ে যাচ্ছে এদের দূস্টান্তমুলক শাস্তি দেয়া উচিত,0,religion
নাউযুবিল্লাহ্,0,religion
কে ভন্ড কে ভালো তুই বেটা বোঝো?,0,religion
এসব ভন্ড রোস্ট করা চালিয়ে যান। কারণ এরা ইসলামের শত্রু দেশের শত্রু।।,0,religion
খুব ভালো লাগলো বক্তারা হুজুরকে সাপোর্ট দেওয়াতে,0,religion
আল্লাহ যার সাথে আছে তার কোনো ভয় নাই।,0,religion
সরকার কেন এসব ভন্ডকে গ্রেপ্তার করে না?,0,religion
আল্লাহু আল্লাহু আবার বলে ঘু আল্লা নামে সাথে এ কি বলে ঘু হুজুরে খাওয়ানি দরকার,0,religion
কুত্তার,0,religion
ভাই আপনি ওকে জূতা মারার বেভছতা করুন,0,religion
দেওয়ানবাগী কাফের তাকে জুতা মারি,0,religion
নেড়ারা হারাম জাদা উনি কি?। এসব হুজুরকে ভয়কট করুন। হুজুরের মাঝে তো আখলাক নেই।,0,religion
যত্তসব পালতু পোলাপান এসব হলো কিয়ামতে আলামত,0,religion
সুলতানা কামাল সত্যিই নাস্তিক।,0,religion
পাগলে পাগলে দেশ তিতা হয়ে গেছে,0,religion
তারা যে কত বড় বোল করছে তারা নিজেও জানে না।,0,religion
ভুল একটি কথা বলছেন যে দেওয়ানবাগীকে কিছুই করা যাবেনা। আসলেই কিছু না অনেক কিছুই করা যাবে যদি আমরা চাই।,0,religion
নাস্তিক কে জুতা মার,0,religion
গরু এটা কোথায় থেকে আসলো,0,religion
এই ছেলেটা আসলেই একটা ফটকা।,0,religion
আমি পাইলে তার গুদ ছিড়া দিতাম,0,religion
ভন্ড কত্তো প্রকার ও কি কি?,0,religion
এদের পাথর মেরে মেরে শেষ করে দেওয়া হক,0,religion
ওর বাবা কয়টা?,0,religion
আপু আপনার কথা গুলা ভালই লাগ্লো,0,religion
ভন্ড তাহেরী পীর এর কি বিচার সরকার করবেন না,0,religion
এই তুমি তো একটা পিচ্চি তোমার মুখে এ কথা মানায় না তুমি বাবা মার কাছে যাও ভালো করে দুধ পান করে বড় হোক তারপরে এস,0,religion
গান না জিকির বুঝলামনা,0,religion
দেয়ান বাগিরে জোতাদিয়া পাটয়,0,religion
ভাই তোর বাল আর দাড়ি না গজাইলে আমার কাছ থেকে কিছু ধার নিস,0,religion
তরে পাইলে জুতা মারতাম,0,religion
ভিডিওটা চমৎকার হয়েছে।এদের মুখোশ খোলে দেন ভাই।তবে টা জায়গায় বুঝিনি।হাফিজুর রহমান সিদ্দিকি আর চরমোনাই এর হুজুর এর বিষয়টা একটু বুষিয়ে দিবেন দয়া করে,0,religion
মিযানুর রাহমান আযহারি খুব ভালো,0,religion
এক হালায় কোরআন মানে হাদীস মনে না আল্লাহ মানে রাসূল মানে না মামুনুল হক বলেছে হাদীসের কথা আর ওই হালায় বলেছে কোরআনের দলিল । হালায় হয়তোবা জানে না কোরআন আর হাদীস এই দুই টাই ইসলাম ও মুসলমান দের দলিল ।,0,religion
তোরে👠👠👠👠👠👠👠👠👠👠👠👠👠,0,religion
আমার মনে হয় চীন দেশকে দূরত্ব বোঝানো হয়েছে,0,religion
দেহ এবং রুহ দুইটা আমদের একসাথেই বসবাস করে। আমাদের দেহের ভেতরেই রুহ । ঐ খাচার ভেতরেই পাখি পাখির ভিতরে খাঁচা নয় । এই রুহ আমাদের ভেতরে থাকা অবস্থায় আমরা যদি আমাদের ভাল কর্মের দ্বারা এবাদত বন্দেগীর দ্বারা অধিক মোরাকাবা মোশাহেদার দ্বারা আমাদের দেহকে যদি রূহের আলো দ্বারা আলোকিত করতে সক্ষম হই তখন দেখা যাবে রূহের সাথে সাথে দেহও পবিত্র হয়ে গেছে । সূফি সম্রাট হযরত শাহ্ দেওয়ানবাগী মাঃআঃ,0,religion
হিজবুত তাওহীদের গোমরা প্রকাশ করার জন্য অনুরোধ করা হল,0,religion
ওদের মুখে ঝাটার বারি মার,0,religion
হুজুর এখন গান গাই কেন?হে নিজেই বেদাত।।,0,religion
খুব খুশি হয়েছি ভন্ডদের মুখোশ খুলে দেয়ার জন্য।জানুয়ার দাবি করে নবি করিম স কিন্তুু সে বলে তার বউ নবীজির মেয়ে ফাতেমা সেটা কিভাবে হয়। নাউজবিল্লাহ।,0,religion
ভাই ওরাতো মনে হয় গাজা বেশি খেয়েছি।,0,religion
ওয়াজ নিয়ে এখন বাবসা করছে বক্তা রা,0,religion
দেওয়ানবাগীর যে সাইজ যে চেহারা কেমনে যায়গায় ধরব চাঁদে😂,0,religion
হায়রে জনগণ এতগুলা মানুষ থাকা সত্ত্বেও হুজুররে এ কিভাবে অপমান করে আপনাদের সামনে ওর হাতটা কাইটা ফালা,0,religion
ও একজন মায়ের সন্তান।ঐ কুকুরে কত বড় বেয়াদপ একজন আল্লাওয়ালা বক্তার সাথে চরম চরম বেয়াদবী।আমি স্বংঙ শাহা জালাল রা মাজার দখিনে গাজার গন্দে আর আগাইতে পারলামনা।আটরশি মাজভান্ডার অনেক অনেক।ঐকুকুর নিশ্চয়ই ঐগ্রপের একজন।ওরে জুতানয় জুতার মালা গলাতে কমিটি আটকাইয়া দিলে বড়খুশি হতাম।আল্লার কালাম থাকলে এমন করতে পারতোনা।,0,religion
ভাই জুতা আছে আপনার কাছে?? আসেন কবরে গিয়া তারে উৎসর্গ করি,0,religion
কোন এক সময় এই দেওয়ানবাগীকে রাস্তায় ফেলে কুকুরের মতো পেটানো হবে আর এ সময় আসবেই আসবে ইনশাআল্লাহ,0,religion
এই ছাগলের বাচ্চা অল্প বয়সে পাখি লে বলা দুঃখ থাকে চিরকাল,0,religion
🐐🤡নাউজুবিল্লাহ 🐕🐘আস্তা একটা🐂 ভন্ড 🐕🐷,0,religion
জারজ,0,religion
এভাবে ভন্ডদেরকে জায়গায় ব্রেক করতে হবে ইসলাম থাকবে ইসলাম আছে আল্লাহু আকবার নারায়ে তাকবীর,0,religion
ভণ্ড তোকে যদি আমাদের ভারতে এমন এমন মানুষ দেখে তাহলে তোকে কিছু শিখিয়ে দেবে।,0,religion
তাহিরি একটা ভন্ড পীর,0,religion
মামলা মনে হয় নিজেদের চাল,0,religion
চার নাস্তিক,0,religion
এখনতো তাহেরী ভালো হয়ে গেছে তাহেরি কি এখন কাউকে গালি দেয় কাউকে বকা বাধ্য করে তারপরও ছোট তুমি তাকে বকা দিচ্ছ শোনো আগে যোগ্যতা অর্জন করো তারপর অন্যকে বলবা ঠিক আছে বেয়াদব,0,religion
কাহা রে বলতাছি ওয়াজ তো করছেন দয়া করে কমেন্ট গুলাও পড়েন !!!😂😂😂 কাকা ফেমাস না হইয়া খামোশ হয়ে যাইবা !!!😢😢😢,0,religion
শালা তুই গিবতকারী,0,religion
আটা বালোনা,0,religion
আপনে বনড মির জাগা পাছেন বাল হয়ে জান,0,religion
ভাই এগিয়ে যাও,0,religion
মদ খা 😂😂 কি কশ না কশ,0,religion
হায় হায়রে মুসলমান শেষ নবীর উম্মত হইয়া তোরা নাস্তিক হইয়া গেলি।,0,religion
জানোয়ার মাজার পুজারী,0,religion
ভাই আপনার এই ছোট্ট প্রতিবাদ ঈমানের একটি বড় পরিচয় বহন করে। দোয়া করি আল্লাহ আপনাদের মর্যাদা আরো বাড়িয়ে দিন। আমিন,0,religion
আমি মিজানুর রহমানের সব ওয়াছ শুনি মিজানুর রহমানের বালো কথা বলে । আব্বাসি বন্ড বন্ড বন্ড,0,religion
হানডেট পারসেন গাঁজা খায়,0,religion
এদের হুক্কর হুক্কর কি করে হারামিরা আল্লাহ বয়ই না মনে আল্লাহ,0,religion
আজহারি হুজুর টিক কথা বলেছেন,0,religion
আপনি ঠিক বলেছেন।তবে আপনি মহিলা হয়ে আপনার কন্ঠ এত পুরুষ মানুষকে শুনাচ্ছেন এটা কি গুনাহ হচ্ছেনা,0,religion
মাশাল্লাহ একাই জনের সাথে লড়ে যাচ্ছে।নাস্তিক হাজার জন হোক না কেন আল্লাহ পক্ষ থেকে একজনই যথেষ্ট।,0,religion
দেওয়ানবাগী যে ভন্ড এতে বিন্দু মাত্র সন্দেহ নেই।আলহামদুলিল্লাহ্‌,0,religion
নাস্তিক তিনটা খেপেছে,0,religion
আল্লাহ তাকে ক্ষমা করবেন না,0,religion
ভন্ড কমিটি আর ভন্ডদের ই দাওয়াত দেয়।,0,religion
বেডা ত ভন্ড এটা আবার নতুন কি,0,religion
আমির হামজা ধন্যাবাদ মুফাছির,0,religion
আগে জুতা মার,0,religion
ঠিক আছি,0,religion
আবনার বাচ্চারা,0,religion
ভিড়িও টা ভালো লাগল,0,religion
এই রকম টকশো থেকে বিরত থাকবেন ওস্তাদ মামুনল হক সাহেব পুরুষ উপস্থাপনা থাকলে যাবেন,0,religion
ভাই অনেক দিন পরে ভিডিও পেলাম ভালো লাগলো,0,religion
হে লোক সাবধান! কিসের জন্য তুই মাওলানা হাফিজুর রহমান ছিদ্দীকির বদনাম করছ? আল্লাহকে ভয় কর,0,religion
ভালোবাসার আরেক নাম মিজানুর রহমান আজহারী,0,religion
আল্লাহ আপনি চার নাস্তিক কে হেদায়েত করুন নয়তো ধ্বংস করে দিন।,0,religion
আমি কিছুদিন আগে শাহজালাল শাহপরান এর মাজার জিয়ারত করে আসলাম কত সুন্দর দোআ দরুর জিকির আজগার চলে হুজুর যে বলছে গাজা খায় এটা একবারে মিথ্যা কথা বানোয়াট কথা বার্তা বলাই এদের কাজ,0,religion
মিজানতো খোদা রসূলের দুশমন।,0,religion
আপনার উপস্থাপনা অনেক সুন্দর ভাই য় হানিফ সংকেত,0,religion
ছবি সামনে রেখে নামাজ পরা একপ্রকার শিরক,0,religion
হা,0,religion
গিবত করা আর ম্রিত ভাই এর গস্ত খওয়া সমান,0,religion
কোন কুলাংগারগুলো ডিসলাইক দেই।,0,religion
নাচতিক লোপা মরে দেক তোর কি হয় বিয়াদপ,0,religion
হুজুর ঠিক কথা বলছে,0,religion
দেওয়ান বাগী পীর না সে একটা ভন্ড শয়তান,0,religion
জুতা মারো 👠👠👠👡👡👡👞👞👞,0,religion
চামে চামে এই হুজুর দয়াল বাবার ভন্ড গানগুলো গাইলেন এইসব হুজুররা বড় ভন্ড আলেম রুপি শয়তান ওদের পেটানো দরকার,0,religion
সরকারের চোখে এগুলো পড়ে না টাকা দিয়ে চোখ বন্ধ করলেই কি দেখা যাই হিন্দু ধর্মের নামে কিছু যদি বলে তাহলে সরকার চুপ করে থাকে না নুরানি দাড়ি ওয়ালা ও মাথায় সুনাতি টুপি ওয়ালা ভাইদের থরে সিবির বলে চালাই দেবে,0,religion
এই সয়তানের দোসর কেয়ামত কোন বন্দরে অনুষ্ঠিত হবে যেখানে তুই জাহাজ নিয়া যাবি,0,religion
বেটা হাদিস টা শামায়েলে দেখ বেয়াদব,0,religion
পীর এর বাংলা শব্দ হচ্ছে দেবতা আল কোরআন কিংবা হাদিসের কোথায় পীর শব্দটি নেই দরগায় কিংবা মাজারে মানত করা হারাম আমরা সবাই যদি সহীহ হাদিস গুলা পড়ি তাহলে এসব যে বেদায়েত তা জানতে পারবো কারন আল্লাহ তায়ালা শীরক কখনো ক্ষমা করবে না,0,religion
আমি যদি সকাল বিকাল থাপরাইতে পারতাম কি যে মজা পাইতাম এই সব ভন্ডদের,0,religion
সালারা জতসব ভন্ড,0,religion
একি সমস্যা কি বাংলাদেশের,0,religion
তোর জন্মের দোষআছে,0,religion
আলহামদুলিল্লাহ। আজান টা শুনে অনেক ভালো লাগলো। 😍😍আপনার ফুল আজান চাই😌😌,0,religion
অস্তাগফিরুল্লাহ,0,religion
হে আল্লাহ তুৃমি তাহেরী কে হেদায়ত নসিব করো জাতে এই বন্ডামি ছেরে দিয়ে ভালো কথা বলে,0,religion
ভাই আমি ইন্ডিয়া থেকে বলছি শালার পুত কে জুতা দিয়ে মার ভাই,0,religion
আল্লাহ তাকে হেদায়েত দান করে,0,religion
অই,0,religion
হে আল্লাহ অদের কে ধংস করে দিন,0,religion
বাছতে চাইলে বালু হয়ে যা,0,religion
তাহেরির আরেকটা জিকির খেককু খেককু খেককু এটা আসলে আল্লাহর জিকির না কুকুরের জিকির ছি ছি,0,religion
আল্লার রসুল সল্লাল্লাহু আলাইহি ওয়াসাল্লাম কি দারি কাটিং করছিলো?? বন্ড?,0,religion
হাফিজ সাহেব আপনার ওয়াজ করা দরকার কুফরি শিরক বিদাতের বিরুদ্ধে অথচ আজহারির জনপ্রিয়তা দেখে আপনার চুলকানি শুরু হল।বড় পেটটা হিংসায় ভর্তি।,0,religion
সালাম বোস,0,religion
আমাদের ভাইবোনরা তোমাদের মরনের চিন্তা নাই????,0,religion
আমির হামজার যদি সত্য বাদী হতো তাইলে সে আর ওয়াজ করতো না।আজ দেখি আমির হামজা মিথ্যা বলে।তাদের কাছথেকে কি শিক্ষা নিবে সাধারণ মানুষ।আমার পাশের জেলায় তার বাড়ি যদি কোনো দিন সামনা সামনি পাই।তাই জিজ্ঞেস করবো।মিথ্যা কথা ছাড়তে পারেন নাই ও ওয়াদা রাখতে পারেন তাইলে কেনো ওয়াজ করেন।আপনেতো নিজেই পথ হারা।তাইলে কেমনে আমাদের সত্য শিক্ষা দিয়বেন।,0,religion
ইন্নালিল্লাহ আল্লাহ এইসকল কিছুর বিচার করেন আপনি,0,religion
যিনি উপস্থাপক তিনিতো থাকবেন নিরপেক্ষ। কথা শোনাও যে ভদ্রতা এই বেয়াদবগুলা জানেনা।এ ধরনের অনুষ্ঠানে যারা যৌক্তিক কথা বলে তাদের উপেক্ষা করা হয়।যাদের চিন্তাধারা নাস্তিকতা ভাব ধারায় পুষ্ট তাদের দলকে ভারি করার জন্য বেশী সংখ্যক হায়নাকে আমন্ত্রণ জানানো হয়।আর ওপর দিকে উৎকর্ষ চিন্তা ধারা মানুষ হয় সংখ্যায় কম।যাতে আক্রমণে সুবিধা হয়।,0,religion
যারা তাহেরি গুরোপ তারা তাহেরির বউয়েরে বিয়ে কর,0,religion
আল্লাহ হাফিজুররহমান কে এত উপরে উঠিয়েছেন যে সব জায়গায় তার ওয়াজ।,0,religion
দেওয়ানবাগী ও তাহেরীর গালে জুতা মারো তালে তালে।,0,religion
ভন্ড মাজার পুজারী বদমাইশ পীর মুরিদী ব্যবসার দোকান খুইলা বদমাসি করছ তোরা,0,religion
খেয়াল করেছেন ও যখন বলল যদি আমার বাচ্চা মারা যায় আল্লাহ না করুক যদি মারা যায় আল্লাহ না করুক তুই যদি আল্লাহকে বিশ্বাস না করিস তাহলে বিপদের কথা বলার সময় আল্লাহর নাম নিবি কেনো??,0,religion
ধন্যবাদ তাহসিন ভাই অবশেষে দেওয়ান বাগীকে রোষ্ট করার জন্য,0,religion
তুমি এগিয়ে যাও আরো সেই পার্থনা করছি,0,religion
পারলে বাহাস করেন,0,religion
শালা তাহেরিকে মারার প্রোয়োজন,0,religion
হাইরে মানোস কোতু পাগল,0,religion
কমেন্ট বক্সের মূর্খদের বলি। উনি শিশু না। অনেক পড়াশুনা করেছেন। আমাদের অনার্স লেভেল উনি অনেক আগেই শেষ করেছেন। দেখতে ছোট দেখা যায়। হরমোনের কারণে,0,religion
শালা মিজানুর রহমান তুই পাগল নবিকে বলিস সিক্স পিক,0,religion
জুতোর বাড়িনা ঝাটা দিয়ে পেটানো দরকার,0,religion
বেদাতি ওলীপুরি ভন্ড,0,religion
ইহুদী নাছারারা পবিত্র ক্বাবা ও হযরত রাসূল সঃ এর রওজা মোবারকের ছবি সম্মিলিত জায়নামাজ বিক্রী করে। আর মুসলমানগণ সরল বিশ্বাসে ঐ জায়নামাজকে পায়ের নীচেরেখে নামাজ পড়ে নিজেদের ধন্য মনে করতো। কিন্তু সূফী সম্রাট হযরত দেওয়ানবাগী মাঃ আঃ হুজুর কেবলাজান বলেন এ দুই পবিত্র স্থানের ছবি সম্মিলিত জায়নামাজ পায়ের নীচে রেখে নামাজ পড়া চরম বেয়াদবী। সুতরাং এ জায়নামাজে নামাজ পড়া উচিৎ নয়। তাঁর অভিমত অনুযায়ী বাংলাদেশ টেলিভিশনেও এ জায়নামাজে নামাজ না পড়ার পরামর্শ দেয়া হয়।,0,religion
কে তুই? মাইনষের গিবত কর?,0,religion
মিজানুর রহমান বাংলাদেশের একটি নিয়ামত,0,religion
খুব ভালো লাগলো ব্রো পৃথিবীর এই নিকৃষ্ট কাফের দেওয়ানবাগী কে নিয়ে ভিডিও বানানোর কারনে বর্তমান এই পৃথিবীতে ওর মতো এতো বড় কাফের আর নাই তোমাদের জন্য শুভকামনা রইল আশাকরি বাংলাদেশের সব ভন্ডদের নিয়ে ভিডিও বানাবে,0,religion
কেনো ভাই এসব মৃত্যা কথা গুলো বলে তুরা মুসলম মুসলমানে ঝগরা করাও তুরা মিডিয়ার মোনাফিকরা,0,religion
আমরা সকলে আল্লাহর কাছে দোয়া করব সকল আলেম এবং তাদের অনুসারী এবং সকল মুসলিমকে তাওহীদ জানার মানার তৌফিক আল্লাহ যেন দান করেন আমিন,0,religion
গাঞ্জা কি ভুনা করে খাইছে!😠,0,religion
অাজহারি ভন্ড,0,religion
ছাগল।,0,religion
শু বক্তা কিয়ামতে আলামত,0,religion
ভাইরে কুরআন শরীফ এর চেয়ে হাদিস বড় হল ??? আগে কুরআন তারপর হাদিস কিন্তু দুইটাই গুরুত্বপূর্ণ কিন্তু কুরআন শরীফ আগে আর সুন্নত আদায় করলে ভাল কিন্তু সুন্নত আদায় করা ফরয নয়,0,religion
তুইতো ইবলিসকে আছিস রে ভাই! তোর খোঁজ করছিল ইবলিস। তোর নম্বরটা আমি ইবলিসকে দিয়েদিলাম,0,religion
আমাদের সরকারকে আমরা অনুরুধ করতেছি এই সব ভন্ড দের কঠিন শিক্ষা দেওয়া উচিত,0,religion
বেজম্মার বাচ্ছারা তগো ভইরা দিমু,0,religion
ওতো দেখি সিফাত উল্লাহ্ এর চেয়ে খারাপ।😠,0,religion
তুই কি হুজুর তুর ওয়াজের বয়স হইছেনি,0,religion
ভন্ডদের কারনে আল্লাওয়ালাদের গালীদেয়। চরমনায়কে গালিদেয়।,0,religion
হুই হাই হুই হাই করার সময় ভাবি এত্তগুলি বান্দরের মধ্যে মনে হয় একটা গাধায় ডাক পারতাসে।,0,religion
আমার খুব খারাপ লাগছে এই দৃশ্যটা দেখে। ভিডিও টা দেখি নাই। কারণ এদের মুখ দেখতেও ঘৃণা হচ্ছে। আল্লাহ এদের উপযুক্ত শাস্তি দিবে আখিরাতে। এ বিষয়ে কোনো সন্দেহ নেই।,0,religion
খুব ভাল লেগেছে,0,religion
ভাই ওরকথা শুনলে আমার শরীরে পেশার ওঠেযাই ওরে যদি একবার পাইতাম। ।শালার মাথার তার সব কইটা ছিড়া।,0,religion
আমি যেখানে নামাজ পড়ি তার সামনে একটা ক্যালেন্ডার ছিলো আর ঐ ক্যালেন্ডারে দুইটা মানুষের আঁকা ছবি ছিলো ক্যালেন্ডার ই খুলে ফেলছি । ছোট বেলা থেকেই শুনছি যে ছবি থাকলে নামাজ হয় না।,0,religion
ইসলামের প্রতি যাদের ভালবাসা নাই এরকম বেয়াদবদের নিয়ে কিসের আলোচনা? আবালের দল,0,religion
ইসলাম পচারের সার্তে সেনেলটি সাস্কাইব করবেন,0,religion
মিজানুর রহমানের চেয়ে ভালো বক্তা আর হবে না এতএব যার সোমেচলোনা বেশি তার চেয়ে ভালো মানুষ আর কেউ না আল্লাহ ভরসা রাখে আল্লাহ মারে কে,0,religion
আমিও ভালবাসি,0,religion
দেশে জঈি না মেরে আগে এদেরকে মারা উচিত,0,religion
কেযামত বেশিদিন নাইত,0,religion
মিঃ সাইফ রচনা আপনার এই সুন্দর ভিডিওটির মাধ্যমেও যদি সুমহান আর শিক্ষিত জনাব আজহারী সাহেবের সিক্স প্যাক বক্তব্যর খুলাশা হয়ে যায় তাহলেই আমি ব্যক্তিগতভাবে অনেক খুশি হবো জনাব আজহারী সাহেব আমাদের নবীর শারীরিক গঠন আর সৌন্দর্যকে ফুটিয়ে তুলতেই এই জামানার সৌন্দর্যমূলক আর উদাহরণ সরুপ সিক্স প্যাক বাক্যটি ব্যবহার করেছেন কিন্তু এখন মুখ খারাপ করে বলতে হয় আমাদের দেশের কিছু মাদারচোদ ভন্ড আর কাফেরদের সাথে তালেতাল মিলানো বক্তা আর কিছু অতি উৎসাহিত মুরিদ আর জনগন আছে তারা নিজের নির্বাচিত মূর্খ বিনোদিত ভন্ড ফালতু টাইপের বক্তাকে প্রভুতুল্য পিত্রৃতুল্য মনে করে পুরো সম্পুর্ণ বক্তব্য না জেনে বুঝেই আজহারী সাহেবকে এটা ওটা বলে বিলাপ করছে তারাই কাফের আমার বিশ্বাস জনাব আজহারী সাহেবের মত শিক্ষীত জ্ঞানি যুক্তিবাদি ধর্মপ্রচারক আর আলেম মানুষ এই সোনার বাংলায় অদূর ভবিষতে আগামী বছরেও কেউ আসবে কিনা আমার সন্দেহ রয়েছে আরে যারা নিজেদের পছন্দের পীর বক্তা আলেমের কথা চোখ বন্ধকরেই বিশ্বাস করে অন্য একজন সুমর্যাদা বক্তাকে কাফের বলে তারাই আগে নিজেদের বক্তা আর গীবতকারীর শিক্ষাগত যজ্ঞতা আর জ্ঞানের পরিশিমা দেখুক জনাব আজহারী সাহেব অনেকগুলি ভিডিওতে এই সিক্স প্যাক বাক্যটির অনেক রকম উদাহরন দিয়েছেন আর যুক্তি দিয়েছন কিন্তু সালা মাদারচোদরা শুধু সিক্সপ্যাক বাক্যটি নিয়েই এমন করছে যেন জনাবকে ফাসিতে ঝুলালেই তাদের আর তাদের ভন্ড মূর্খ বক্তারা সফলতার ট্রফি কাপ মেডেল পাবে বাইনচোদরা ধন্যবাদ সাইফ ভাই এমন ভিডিওর মাধ্যমে সত্য মিথ্যার ব্যবধান করে দেওয়ার জন্য আর আমার মুখের কিছু উনুচিত ভাষা ব্যবহার করার জন্যও আপনাদের কাছে ক্ষমা প্রার্থী আর এখনো যারা আজহারী সাহেবকে কাঠগড়ায় দার করাতে চান তাদেরকে আবারো বলছি নিরপেক্ষ ভাবে আজহারী সাহেব সিক্সপ্যাক বাক্যটি কেনো আর কি উদ্দেশে ব্যবহার করেছেন তার অনেক রকম যুক্তি উদাহরণ আর আরও সুস্পষ্ট ভাবে উপস্থাপন করেছেন।। আশা করি দেখলে নিঃশ্চয় আপনাদের ভুলও ভেংগে যাবে,0,religion
গাজাখোরদের গায়ে জলবেই,0,religion
আল্লাহ আমাদের সব ধরনের শিরক থেকে হেফাজত করুক!,0,religion
সালা জেই মোটা ওর কদম এর নিচে পরলে বাচব। 🤣🤣🤧🤧,0,religion
ভাই আল্লাহ ও আল্লাহর রাসুলকে যে হালা বলে সে জত বর এলেমদার হোক তার সব আমাল বরবাদ।।।হাদিসে আছে সেস জামানায় এমন আলেম থাকবে জাদের কন্ঠ শুনে মানুস পাগল হবে এবং তার দলভুক্ত হবে।।।অনেক এলেমের অধিকারি হবে কিন্তু ছোট্ট কুফুরির জন্য তার ইমান থাকবে না।।।কোরান হাদিস জাইন্না ফতোয়া দিস।।তুই দাওয়াত ইসলামির ভিডিও দেহিস তাইলে বুজবি আঝারির ঈমান আছে নাকি,0,religion
এই কাফেরকে হত্যা করা উচিত,0,religion
ঠিক বলেছে আমির হামজা,0,religion
কিংগোপলি 🙄,0,religion
অনেক দিন পরে ইন্টো টা দিয়েছেন। ভালো লাগলো,0,religion
মাওলানা মামুনুল হককে একটা প্রশ্ন আপনি এই খবিশ নাস্তিক মুরগি কবির মুরতাদগুলোর গোল টেবিলে কেন গেছেন ? আল্লাহ কে যারা মানে না কোরআনের আইনের বিরুদ্ধে যারা সারাজীবন যুদ্ধ করে আসছে । তারা আপনাকে শুধু হেইপ্রতিপন্ন করছেনা সমগ্র মুসলমানদের অপমানিত করছে। আপনি জাকির নায়েক হতে চান ।তবে নিজের একটি টিভি চ্যানেল খুলুন। যেখানে শুধু আপনার কতৃত্ত থাকবে। ওরা আপনাকে ওখানে নিয়ে গেছে মুসলমানদের মাঝখানে বিভেদ সৃষ্টির জন্য।,0,religion
এটাই মনে হয় কেয়ামতের আগের দৃশ্য।,0,religion
কথা কিন্তু সথ্য,0,religion
জোতা মারা দরকার,0,religion
হাসি থামাতে পারলাম না,0,religion
উপস্থাপক সহ বাকি তিন জন ই হইলেন পরিপূর্ণ গাধা। মামুনুল হক সহেব আপনি যতই এদের কে বুঝান না কেন তারা বুঝবেনা।আর আমি মনে করি এদের মধ্যে কারোই কোন যোগ্যতা নাই আপনার মতন একজন মানুষের সামনে বসে কথা বলার।আল্লাহ আপনার সম্মান কে আর বারিয়ে দিন,0,religion
যখন চারটা কুকুড় একজন মানুষকে কামড় দিতে চায় তখন মানুষটি আল্লাহু আকবর বলে এগিয়ে যাবে ইনশাল্লাহ!,0,religion
এসব নাস্তিকদের সামনে পাইলে এদের প্রত্যেককে জনসভায় ফাঁসি দিতাম,0,religion
ওস্তাদ আপনাকে স্যালুট জানাই,0,religion
এই লিস্টে যারা আছে তাদের দু’জনকে হত্যা করা হয়েছে। দু’জনকে দেশ ছাড়া করা হয়েছে। দু’জন নিজেই মরে গেছে। যথেষ্ট নাস্তিক হত্যা করা যায় নাই। ভাই বাকিদের লিস্টও প্রকাশ করেন। তারপর তাদের তো হত্যা করবেন সেটা জানা কথা। যদিও সিরিয়ায় আপনারা হেরে গেছেন তবু অনেক গোপন অস্ত্র আপনাদের কাছে এখনো আছে। আর এতগুলি আস্তিককে যেই সরকার ফাঁসি দিলো সেই সরকারের প্রধানকে এই লিস্টে দেয়া হয়নি কেন? তাকে হত্যার চেষ্টা তো আপনারা করছেন অনেক দিন ধরে। ইমান দুর্বল হয়ে গেছে নাকি?,0,religion
হুজুর টিক বলছেন,0,religion
মজা আর মজা,0,religion
এখানে দন্দের কি হলো বাহাদুরি দেখিয়ে উনি চলে গেলেন।,0,religion
ওপমান কথাটি লিখে আব্বাছি হুজুর কে ছোট্ট করলেন মিডিয়া ভাই কথাটা কাটলে ভালো হয়,0,religion
ধন্যবাদ ভাই ভালো লাগে ল,0,religion
আপনারা জানেন কী? হাদীস শরীফে বলা হয়েছে “যে পবিত্র কুরআনে এরশাদ হয়েছে “যাদের ক্বালব আল্লাহর জ্বিকির থেকে গাফেল রয়েছে তারা প্রকাশ্য গোমরাহ্ বা পথভ্রষ্ট” সূরা যুমার আয়াত । তাই সূফী সম্রাট হযরত দেওয়ানবাগী মাঃ আঃ হুজুর কেবলাজান মানুষকে ক্বালবে আল্লাহর জ্বিকির জারিরর শিক্ষা দিয়ে গোমরাহী থেকে উদ্ধার করে ঈমানের পথে চলার শিক্ষা দেন। মহান আল্লাহ্ তায়ালা এরশাদ করেন “তোমরা যখন নামাজ শেষ কর তখন দাঁড়ানো বা বসা ও শায়িত অবস্থায় আল্লাহর জ্বিকির কর” সূরা নিসা আয়াত । মহান আল্লাহ্ তায়ালার এ নির্দেশ পালন করে মানুষ যাতে সর্বসময় ক্বালবে আল্লাহর জ্বিকির জারি রেখে অজ্ঞান অবস্থায়ও ঈমানের সাথে মৃত্যু বরণ করতে পারে এজন্য তিনি মানুষকে সার্বক্ষণিকভাবে ক্বালববে আল্লাহর জ্বিকির জারির শিক্ষা দেন।জে দুনিয়ার চিন্তা আসে সে নামজ কবুল হয় না।” মুমিন মুসলমানগণ যাতে দুনিয়ার চিন্তামুক্ত হয়ে একাগ্রতার সাথে আল্লাহ তায়ালাকে হাজির নাজির জেনে নামাজ আদায় করতে পারেন সূফী সম্রাট হযরত দেওয়ানবাগী মাঃ আঃ হুজুর কেবলাজান সেই পদ্ধতি শিক্ষা দেন। তাঁর নিয়ম অনুসরণ করলে মুসুল্লীদের নামাজে দুনিয়ার কোন চিন্তা আসে না। ফলে তারা নামাজের পরিপূর্ণ ফায়েজ বরকত ও রহমত হাসিল করতে পারেন। এমনকি কেউ কেউ “নামাজ মু মিন ব্যক্তির জন্য মে রাজ” এ হাদীসের বাস্তবতা উপলব্ধি করতে সক্ষম হন।,0,religion
হুজুরের পাগরি যত বড়ই হোক না কেনও নবীকে মানলে জান্নাত না মানলে জাহান্নাম। হাফিজুর হুজুরের পতিটা কথায় ভুল আছে মিনিটে মিনিটে,0,religion
আমি তুমাদের সাথে আছি,0,religion
লোপা তোর কথায় ইসলামের কোন কিছু যায় আসে না। তোর মতন অনেক নাস্তিক আছে। তার একটা কথা বললেই ইসলামের কোন কিছু করতে পারবি না। আল্লাহ তাআলা নিজেই তার কোরআনকে রক্ষা করিবে। তোর মতন লোপা কত গেল কত আসলো।,0,religion
তাহিরি শালা ভন্ড,0,religion
এই হারামিকে পাইরালা,0,religion
ওরা এখনো ভুল পথে আছে জাতি কি শিখবে সহি কোরআনের আলোকে দাওয়াত দিয়ে মানুষকে হেদায়েতের,0,religion
আহলে হাদিস দের মুল উদ্দেশ হল আলেমদের কা্জ থেকে দূরে সরানো্‌ কারন ওরা শয়তানের দুশর কারন এলেম শিখা ফরজ আর সতানের কাজ হল এলেম থেকে দূরে সরানো্‌ ।।,0,religion
তোরা ভন্ড,0,religion
এ ভন্ড,0,religion
এভাবে কতজন শিশু বক্তা ভন্ড,0,religion
আমাদের প্রধানমন্ত্রী শেখ হাসিনা কি মুসলমান নয় ?দেওয়ানবাগী তাহেরী যে এইসব করছে তিনি কি এগুলো দেখেন না ?এগুলো দেখেও তিনি তাদের বিরুদ্ধে ব্যবস্হা নেন না কেন ?আমার মনে তিনি বাংলাদেশের প্রধানমন্ত্রী হলেও ইসলাম সম্পর্কে তিনার নূন্যতম জ্ঞান নেই নাকি তিনি দেওয়ানবাগী তাহেরী তাদের কাছ থেকে মোটা অংকের টাকা পায় ?যার ফলে তিনি তাদেে বিরুদ্ধে কোন ব্যবস্হা নেন না আর বাংলাদেশে ধর্মমন্ত্রী থাকার কোন যৌক্তিকতা আছে কি ?,0,religion
মাশাহ আল্লাহ উনিতো এটা বাঘের গর্জনই দিলেন !,0,religion
কোন বাচ্চা পংগু হয়ে জরম নিলে অপরাধটা কার?,0,religion
বিয়াদব কোথাকার।।আগে শিক্ষিত হ তারপর বক্তব্য দে।,0,religion
আললাহকে ভয় কর,0,religion
আল্লাহ গজব দাও,0,religion
বাংলাদেশের কিছু আলেমরা মাহফিল মন্চে উঠেই তাদের প্রথম কাজ হলো সমলোচনা করা,0,religion
সূরা ইখলাস সূরাঃ আয়াতঃ বাংলায় অনুবাদঃ বলুন তিনিই আল্লাহ্ অদ্বিতীয়! আল্লাহ অমুখাপেক্ষী । তিনি কাউকে জন্ম দেননি এবং কেউ তাকে জন্ম দেয়নি। আর তাঁর সমকক্ষ কিছুই নেই!,0,religion
এরা সেই হুজুর নামধারী ভন্ড যারা ঘুষ কে হাদিয়া বলে গ্রহন করে।,0,religion
তর মত লোক কি বুঝবি ইসলাম সমন্ধে,0,religion
ওরে গু মাখা পিছা দিয়ে বাড়ি দে,0,religion
তাহেরী না তুই ভন্ড,0,religion
বছর জেল চাই ভন্ড তাহেরীর।,0,religion
মিজানুর রহমানকে নিয়ে এরুকুম বলবেন নাম।আমি বছরের মেয়ে। আমি মিজানুর রহমান আজহারির ওয়াজ শুনি তাই বুজলাম আপনারা মিথ্যা কথা বলছেন,0,religion
নাউজুবিল্লাহ আসতাগফিরুললা,0,religion
এই রকম ঝাকাঝাকি ইসলাম ধর্মের কোথায় আছে? অদ্ভুত লাগে! ফালতু আশেকের দল,0,religion
মিথ্যা তো তারাই বানায় যারা আল্লাহর নিদর্শন সমূহের ওপর ঈমান রাখে না। বস্তুত তারাই মিথ্যুক। সূরা নাহাল যার মধ্যে মনুষ্য রুচিবোধ কিংবা সুস্থ প্রকৃতি বিদ্যমান সে কোনক্রমেই মিথ্যার প্রতি সমর্থন জ্ঞাপন করতে পারে না। মিথ্যা একটি চারিত্রিক ব্যাধি। মিথ্যার প্রতি সমর্থন না করাই হচ্ছে স্বাভাবিক মনুষ্য ধর্ম। সকল ধর্মেই এর প্রতি নিন্দা জ্ঞাপন করা হয়েছে।,0,religion
জানয়ারের বাচ্চা,0,religion
সয়তান তাহিরি,0,religion
ভাই আপনাকে দন্যবাদ,0,religion
অসংখ্য ধন্যবাদ আপনাকে।,0,religion
নাউজুবিল্লাহ 😡,0,religion
উপরওয়ালা বলা যাবেনা। আল্লাহকে।,0,religion
নাস্তিকদের থেকেও ভয়ানক এসব ভন্ড রা। এদের কে ইসলামি আইনে বিচার করা দরকার। এদের কারনেই আজকের সমাজ দেশ ও জাতির এই করুন অবস্থা। আর আমাদের মত মুরখ মানুষ রা কেনো জায় তাদের কাছে??,0,religion
ইসলামের মহা গবেষক এবং সমালোচক জ্বনাব মুফাস্সিল ইসলামকে বিভিন্ন ধর্মীয় ডিবেটে ঐতিহাসিক বিজয়ী ঘোষনা করা হয়েছ।ইনিই হচ্ছেন পৃথিবীর ইতিহাসে সর্বকালের সর্বসেরা ভয়ঙ্কর নাস্তিক।প্রধান চারটি ধর্মের মধ্যে ইসলামকেই বেশী ভোগাছ ফাল্তু এবং ভিত্তিহীন বলে তিনি মনে করেন।,0,religion
গাঞ্জা বা হিরোইন না ভাই।।নতুন একটা নেশা করে সে 🤣🤣,0,religion
এদের বিরুদ্ধে দ্রুত আইনি ব্যবস্থা নেয়া উচিৎ,0,religion
আসসালামু আলাইকুম ওয়া রাহমাতুল্লাহি ওয়া তা য়ালা ওয়াবারাকাতুহু সম্মানীয় বক্তা সাহেব আপনি যেটা বলেছেন সেটাই সঠিক আমার নিজের চোখে দেখা শাহজালালের মাজারের পশ্চিম পাশে সোনালী কালারের কই মাছের ওইখানে একটা রুমের মত বানানো আছে যেটার সামনে খোলা সেইখানে গান বাজনা হয় এবং কি গাজা খাওয়া হয় আর মেন গেটে প্রায় একটি পাগলি বসে থাকে ঐখানে পায়খানা করে এবং কি বেশি সময় তার পরনে চাদর থাকে পায়খানা লেগে থাকে আমি নিজে দেখেছি সেই জন্য আমিও আপনার সাথে একমত তবে মাজারে যারা ওলী শুয়ে আছেন তাদের কোন দোষ নেই দোষ মাজার সভাপতি যারা হয়েছেন এ আজকালের যুগে তাদের মাজার কে পুঁজি করে নিজেদের পকেট ভারী করে ঊশৃংখল কাজের প্রতি কোনো বাধা দিয়ে থাকে না কারণ তারা নিজেরাই ও শৃঙ্খলা পছন্দ করে আপনার পাশের যে ব্যক্তি টা জোর দিয়ে নামিয়ে দেন স্টেজ থেকে তার কোন অধিকার নেই একটা ওয়াজ মাহফিলে অতিথির গ্রহণ করে এই সমস্ত বন্ধুদের কারণে বাংলাদেশ বর্ণনা করা যায় না,0,religion
লোপা রহমান তুমি ইসলামের কোন ক্ষতি করতে পারবেনা ইনশাআল্লাহ বরং তোমার ইহকাল ও পরকাল দুটোই তুমি নষ্ট কোরে ফেলছ,0,religion
শালা৷ বাটপার,0,religion
মিজানুর রহমান আজহারি খুব ভালো মানুষ,0,religion
লা ইলাহা ইল্লাল্লাহ পরতে পারে না অনি আবার আলেম,0,religion
মিজানুর রহমান বাংলাদেশের গৌরব। মিজান ভাই আপনাকে ভালো বাসি আমরা।,0,religion
নিজের মধ্যে জগড়া না করে কিভাবে ঈমান কায়েম হবে সেই দিকে দেখা উচিত কিভাবে কোরানের আইন দুনিয়াতে কায়েম হবে সেইদিকে দেখা উচিত আমরা মুসলমান রা নিজের দের মধ্যে ঝগড়া করছি আর বেইমানি কাফের বাতিল সরকার নিজের দের মতো দুনিয়া টা চালাচ্ছে তামাম পৃথিবীর মুসলমান রা যদি একসাথে থাকতো তাহলে তামাম পৃথিবী টা জান্নাতের টুকরো হয়ে যেত যদি আমি কোনো খারাপ কথা বলে থাকি বা কারোর যদি আমার কথা গুলো খারাপ লাগে তাহলে ক্ষমা চাইলাম,0,religion
নাস্তিকরা কবরে যা দেখ আল্লাহ কি করে,0,religion
একটু এসকের জিকির করলো তাতে রেগে গেলেন রাগ জিনিস হারাম আমির হাম্জার দালালি করবেন না তাহেরী সাহেব এর সামনে আমির হামজা কে বসায় দেন তখন দেখা যাকে কে হক্ব ।,0,religion
এই ছোট শিশু বাচ্চা আর কি বলবে। সে তো ভালোমতো কোরআন হাদিসের একটা আয়াত বলতে পারে না,0,religion
আল্লাহ তুমি এদেরকে এমন শাস্তি দিবেন জেন আর কোনো নাস্তিক এমন কাজ করতে সাহস না পাই !,0,religion
শালা মিথ্যুক,0,religion
শাহরিয়ার কবির তর বাবা কয়জন বে ?,0,religion
জুরে কথা ভলানো হয়তাছে,0,religion
এসব ভিডিও আরো বানাও,0,religion
আমির হামজা কে আমি ভালোবাসি,0,religion
এদের কে বিনা জবাবে শাসতি দেও৷ আললাহ,0,religion
তাহেরি তুয় যদি ভারতে আছি তোকে জুতা মারবো,0,religion
আলহামদুলিল্লাহ আমার এই চ্যানেলে নাস্তিকদের বিরুদ্ধে ভিডিও বানাচ্ছি,0,religion
নাস্তিক একজন ভাল মানুষ নাস্তিক দের ফাসি চাই।,0,religion
জ্ঞান অর্জনের সাথে মুর্তির কি সম্পর্ক?? যারা মুর্তির পক্ষে কথা বলে ঐ শয়তানগুলো সত্যিকার অর্থে মুর্তিকে পুজা করে এতে কোনো সন্দেহ নাই।।,0,religion
নাওজুবিল্লাহ এটা মুসলিমদের কাজ না,0,religion
তাহেরীর খ্যাতা কিলাই।,0,religion
এরা মুসরিক,0,religion
আল্লাহ তুমি কোরয়ান কে হেফাজত কর,0,religion
আমাদের বাংলাদেশটা কি যে হবে সেটা আল্লাহ আল্লাহ তায়ালা নিজেই ভালো জানেন কিন্তু দেওয়ানবাগী কি অবস্থা হয়েছে তার একটা মন আজও কবে যায় সেটা আপনিই ভাল জানেন সেজন্য মনে হয় আল্লাহ পাক বাঁচিয়ে রাখছে দেশের মুসলমান সামনের পেটটা বাস্ট করে দিব আল্লাহতালা যেন কবুল করেন এমন ভাবে হয় মানুষ দেখে যেন ভয়ে আতঙ্কে এরকম না করে,0,religion
আমিও দেখেছি,0,religion
আর তরা পোলা পোটকি মারছ,0,religion
এই ভিডিওটা সঠিক হয়েছে কারন এখানে সবাই ভন্ড,0,religion
চার কুকুর যন মানুস,0,religion
তরে জুতা মারার দরকার,0,religion
ভাই সব মাজার ভন্ডনা মাজারকে ভন্ড করে তুলে মাজার পরিচালনা কমিটি আর সেটা কোনো মাজারের দুষ না।,0,religion
একটু অপেক্ষা কর কঠিন শাস্তি তোদের জন্য অপেক্ষা করতাছে,0,religion
আল্লাহ তোমার কাছে বিচার দিলাম তুমি আমাকে উঠিয়ে নেও 😂😂😂😂🤣🤣🤣🤣🤣😂😂😭😭😭🤣😂😅,0,religion
সরকারে ওগো না মারলে আমরা যুবক ছেলেরা মারবো,0,religion
এই মহিলাকে আফগানি দিয়ে ঠিক করা দরকার কি বলেন?,0,religion
আসসালামুয়ালাইকুম ভাইদের ধন্যবাদ,0,religion
গাঁজা,0,religion
এদের কে মাটিতে রেখে জুতা স্যান্ডেল মারা দরকার,0,religion
দেওয়ান বাগীকে জুতা মেরে দেশ থেকে বের করে দেওয়া উচিত।।।,0,religion
রাসুল সঃ বলেছেন “আমার মৃত্যুর পর আমার নামে অসংখ্য মিথ্যা বিষয় প্রচলিত হবে এবং যে আমার নাম দিয়ে মিথ্যা প্রচার করবে সে জাহান্নামে নিজ আবাস তৈরী করবে” বুখারী মিশর ম সংখ্যা পৃ থ খন্ড পৃঃ তিরমিযী ‌ থ খন্ড পৃঃ ইবনে মাযাহ ম খন্ড পৃঃ ভণ্ড মুফতী। আল্লাহ্‌ আমাদের এই সকল ভণ্ড পীর থেকে হেফাজত করুণ। আমীন।,0,religion
মাশাআল্লাহ্ হুজুর শালা ভন্ড মাজার পূজারি,0,religion
এরাই ভন্ঠো এরাই শইতান,0,religion
এইসব ধর্মের নামে ভুয়াভেজাল কথা প্রচারকারী লোকেরা মানুষকে বহুত বিভ্রান্ত করছে এখন বোকা মানুষের সংখ্যা কমতেছে,0,religion
দেখুন মানছি কিছু নামধারী পীর আছে যাহারা ভন্ডামি আর গান বাজনায় ব্যস্ত শাহস থাকলে বড় পীর আব্দুল ক্বাদীর জীলানী রঃ এর নামে কিছু কেহ বলে দেখাক সাহস থাকলে মইনুদ্দীন চীশতী হাসান সানজারী রঃ এর নামে কিছু বলে দেখাক।। শাহস থাকলে শাহ জালাল রঃ এর নামে কিছু বলে দেখাক। পারবে না কারন তাহারা আসলেই হক্কানী আল্লাহর ওলি ছিলেন। এখন কিছু বেয়াদব মওলভী আছে যাহারা এতটাই বেয়াদব যে ওয়াজ করতে এসে কোথায় কে কি করেছে সেই সমালচনা নিয়ে কথা বলে । আবার কিছু আছে পর্দার ওয়াজ খুব পছন্দ তাহারা ওয়াজ করতে গেলে এক বেপর্দা মহিলার  দেহের কোন কোন অংগ বের করে রাস্তায় বের হয় সেই অঙ্গ গুলোর বিবরন দেন। ভন্ড পীর দের যেমন যুতা পিটা করা উচিৎ একই ভাবে ভন্ড মওলানা দের ও জুতা পেটা করা উচিৎ,0,religion
মাল টা কে চু,0,religion
মাদারবোর্ড😍,0,religion
তোর বাল উঠছে তাহেরি কে নিয়ে গিফত করতেছিস,0,religion
নাস্তিকের বাচ্চা তোদের ওপর গজব পড়বে,0,religion
শাহরিয়া কবিরের দুই গালে জুতা মারো তালে তালে,0,religion
তাহেরি একটা ভন্ড। ইসলাম প্রিয় সবাইরে এর বিরুদ্ধে প্রতিবাদ করা উচিত,0,religion
মাজার পুজারীরা মুশরিক।,0,religion
ভাই আল্লাহ আল্লাহ করেন আল্লাহ যেন এইসব নাস্তিক গুলাকে দুনিয়া থেকে উঠিয়া নিয়া জান না হয় হেদায়েত দান করেন,0,religion
ওরে ল্যাংটা করে পিটা ও আমাদের মা ফাতেমাকে অপমান করছে,0,religion
প্রচুর কড়া,0,religion
এই গর্দভগোষ্ঠী যতটুকু জ্ঞান রাখে নিজেদের সাবজেক্টে তার এক দশমাংশ পড়াশুনাও যদি ইসলাম নিয়ে করতো নির্মোহভাবে তাহলে এমন অর্বাচীনের মত কথাবার্তা বলতে হত না। উনাদেরকে বলা উচিত ছিলো আপনারা আগে বেসিক ক্লিয়ার করে আসেন। আর ম্যানার শিখে আসেন কোথাও থেকে ।। নিজেরা কথা বলে যাচ্ছে নিজেরা ঝগড়া করে যাচ্ছে একজন আরেকজনের আগে কথা বলার জন্য ।। সব নাস্তিক মূলতঃ ইসলামবিদ্বেষী ই একেকটা গোঁড়ামির গোডাউন।,0,religion
নারকেল গাছের মাথায় ঠাডা না পড়ে এদের মাথায় কেন পড়ে না,0,religion
আমার আসলে মনে হয় এডমিন তুই মুসলমান নয় কোনো ইহুদির সন্তান হবি ! তোরে আগে জুতা মারা ধরকার !,0,religion
এটা বেশ্যা পাড়া?,0,religion
দুরো ফাগল,0,religion
আমির হামজা বাতিলের আতংক,0,religion
এই মুর্কদের সাতে কতা না বলাই ভালো,0,religion
বাংলাদেশের মানুষ আল্লা রাসূল রেকের ভন্ড দের বিশ্বাস করে এই ভিডিও চাইরা ও লাব নাই।বাংলাদেশের মোল্লা রাই যে কতা বাতা বলে এগোলা সুনলে বাংলাদেশেরে মুসলমান করিয়া পরিচয় হয় না।যার কাচে সিকমো তারা কাচে কি কা সিকি হায় রে বাংলাদেশের লাগি দঃখ হয়।👍,0,religion
শয়তান কি পকার দেখলে বুঝতে পারেন,0,religion
তই কার রে দালাল তাহেহির নাকি দেওয়ান বাগির পারলে সামনে আস দেখি তোর কতো সাহস।,0,religion
ভাই এতো কথা বলে লাভ নেই খোদ প্রধানমন্ত্রী শেখ হাসিনা দেওয়ানবাগী সম্পর্কে কিছুই জানেনা বলে আপনাদের ধারণা। পুলিশ প্রশাসন থেকে শুরু করে সবাই জানে। তাই এই সমাজের এই জাতিয় বিষ ফোরা দুর করতে হলে ঐ একজনই যথেষ্ট আর সে হলো শেখ হাসিনা।,0,religion
আপু আপনি কি আল্লাহর জিকির করেন???,0,religion
কি এগুলো দেখেনা??,0,religion
একজন মুসলিম কে কিভাবে কুলেংগার বলে।ব্যয়াদবির একটা লিমিট আছে🤬🤬 তাহেরি আর তুমার মধ্য কুন পার্থক্য পেলাম না। ব্যায়াদব।,0,religion
একজন বে পর্দা মহিলার সামনে জন নাস্তিক এর সামনে বলার প্রজন নাই।,0,religion
ভিডিওটি ছাড়ার জন্য অসংখ্য ধন্যবাদ তবে এটা ভালো করে প্রচার করুন ভাইয়েরা,0,religion
নাস্তিকে দেশটা ভরে গে ছে,0,religion
তাহেরি সাহেব মানুষদেরকে গমরা বানায় ℅,0,religion
কোরআনে যদি বইসা যান একথা থাকতে পারে।তাহলে এই জালালি কথাটাও কি আছে নাকি!!!!!,0,religion
আরে নবী অলির দুশমনেরা কোনটা গান আর কোনএকটা শান তোরা এইটাই বুজস না তরা আবার কিশের আলেম তরা তো আলেম নামের জালেম এখনো সময় আছে নবী অলিদের কে ভাল ভাসতে শিকোন,0,religion
সব মাজারি বেদাতি,0,religion
ছি মিনার টিভি মিথ্যে বলেন কেন। বক্তাকে কেউ তো মারেনি বরং আপত্তি উত্থাপনকারী কে মারতে উদ্যত হয়েছিল বক্তার সমর্থকেরা।,0,religion
তাহের নাম্বার ওয়ান ভন্ড তাহেরির জদি কোন লজ্জা থাকে তাহলে কোন হুজুর কে নিয়ে কথা বলতোনা তাহেরি একটা কুলাঙ্গার,0,religion
এমন অনেক ভণ্ড পিট্টা মানুষ করছি খালি পাইয়া লই একবার,0,religion
দেশটাতে ইসলাম বিদ্বেষী নাস্তিকে ভরে গেছে,0,religion
তাহারি তুমি যতই চিল্লাহ মারকেট পাবা না।,0,religion
হুজুরের কথা টিক সিলেট সাজা লাল ও শাহপরান য়ের জায়গা এই জায়গায় ওনেক আবাসিক হুটেল কেন কথা টিক হলে লাইক দিন,0,religion
ওর কপালে জুতা মারো বেইমান বাগি,0,religion
জুতিয়ে কপাল ফাটিয়ে দেওয়া দরকার এইসব ভণ্ডদের,0,religion
হে মানুষ আল্লাহকে ভয় কর। তুমি আমি আখেরি নবীর উম্মত। কেন তোমরা হাফিজুর এর বিরুদ্ধে বলো। সে একজন আলেম। আলেমদের সম্মান করতে শিখুন।,0,religion
মাছিহ দাজ্জাইল হোলো দেওয়া বাগী,0,religion
আমি অ গলায় ফাঁস দিয়ে মারতে পারতাম জুদি আমার,0,religion
যে ভন্ড সেই ভন্ডামি কাজ করে।আল্লাহ আপনাকে হেদায়েত দান করুক এ সকল ভন্ড খবর গুলো না দিবার জন্য।,0,religion
তগুর কাম নাই সাসা,0,religion
🤣🤣🤣🤣🤣🤣🤣 মজা পাইলাম 😂😂😂😂😂,0,religion
এই চ্যানেলকে বলতে চাই জনগনের যে ক্রোধ এই জানোয়ারগুলোর প্রতি দয়া করে তাদেরকে জানিয়ে দেন।একটা সময় আসবে মৃত্যুর সময় কুৎসিত হয়ে যাবে।,0,religion
এরা নবির দুস মান,0,religion
রাইট।,0,religion
আব্বাসির আচরণে স্পষ্ট অহংকার প্রকাশ পেয়েছে। ইসলাম এতটা কঠিন নয় যে স্বদিকিন শব্দের অর্থ পীর তা হুজুরের কাছ থেকে জানতে হবে।,0,religion
সত্যর বিজয় হয় একদিন,0,religion
আল্লাহ গজব পরক,0,religion
ঈদে মিলাদুন নবি বেদাত কোন হাদিসে আছে,0,religion
পাগল ছাগলের দেশ।,0,religion
এখানে তিনজন নাস্তিকের বিরুদ্ধে তিনজন আলেম কেন নেওয়া হলো না,0,religion
আল্লাহ আপনে এদের বিচার করেন,0,religion
মার হাবা,0,religion
ওকে কিছু করতে না পারলে ও নিজেকে অন্তত খেয়ালী করতে পারলাম। আর হ্যা তাশিনেসন ভাই আপনি নিজের খেয়াল রাখবেন 😑,0,religion
ঠিক হোক আর ভুল হক জনতা মূর্খতার পরিচয় দেয়,0,religion
ভাই ভন্ডো পির নিয়া ভিডিও বানিয়েছেন ঠিক আছে ধন্যবাদ কিন্তু এখানে ভন্ড পীরের সাথে ভালো আলেম কে কেন জরালেন কাহিনী কি,0,religion
এই মূর্খদের সাথে কথা বলাই উচিত না।,0,religion
ভন্ড ছালা দেৰ কে পিটানৰ দৰকাৰ,0,religion
কেয়ামত বেশি দেরি নেই মানুষ পাপের দিগে ডলে পরছে,0,religion
চারজন,0,religion
আমির হামজা ভুল,0,religion
লানত দেওয়ানবাগীর উপর।ধংশ হোক সে এবং তার অন্ধ ভক্তরা।,0,religion
সব নাস্তিক মুসলিম হা হা হা হা,0,religion
পুরা ভিডিও দেখা জা বুঝলাম তা হলো তুমিও মানুষ কে বোকা বানাচ্ছো,0,religion
আমি বুজলাম না যারা ডিসলাইক দিছে তারা কি দেওয়ান মাগির মুরিদ নাকি,0,religion
তুমি যদি ভালো হইতা তাহলে সাইদিরে চাদে দেখা গেছে সেটা তুলে ধরলানা কেন সেটা সাইদির কেরামতি,0,religion
দেযানবাগি কাইফের কাইফের ভাই ভন্ভ দের বিরুদ্ধে প্রতিবাদ কর আল্লাহ্ ভালো করবে তোমার আমি ইন্ডিয়া থেকেই বলছি ইন্ডিয়া এই রকমের ভন্ভ অস্তোপালি কচুকাটা করব,0,religion
আমার বাড়ির পাশেই শাহজালালের মাজার। গাজার গন্ধে অইদিকে যাওয়াই যায় না। শ্রোতা বৃন্ধকে ধন্যবাদ। শালা মাজার পুজারীকে শিক্ষা দেবার জন্য।,0,religion
শয়তানের বাচ্চারে পিটিয়ে মারতে হবে,0,religion
এইস হুজুর ইসলামের কোন আলোচোনা করে না সমাজে মারা মারি তৈরি করে। এসব হুজুর কে পেলে কাইটা টুকরা টুকরা করে রাস্তায় দাও,0,religion
জাকির নায়েকের সমালোচনা করাটা আমি মনে করি সকল মুসলমানের জরুরি দরকার আর আপনারা কিছু কিছু ভন্ড দালাল সাংবাদিক আছেন সকল ভন্ড পথ ভ্রষ্ট আলেমের সাথে আল্লামা নুরুল ইসলাম ওলিপুরী সাহেবকে একা কার করে ফেলেন ওলিপুরী সাহেব হলেন এই যুগের এক জন মুজতাহিদ মুনাজরে আজম সাইখুত্যাফসির অনেক বড় হক্কানি আলেম এই যুগের আপনারা টাকার জন্য হক্কানি আলেমদের সাথে আর কোন দিন বিয়াদবি করিবেন্না,0,religion
কোনো দেশ কে তো আমি মডেল হিসেবে মানাবো না মডেল হিসাবে দেখবো এবং মানবো আমার রাসূল সাঃ কে আর আইন কানুন মানবো কোরআন এবং হাদিস অনুযায়ী !!!,0,religion
খোদার গজব পড়ুক তোদের উপর,0,religion
চালিয়ে জাও,0,religion
ওদের মুরিদ দের ফেরে ফেললে এগুলা কুমবে,0,religion
আমার প্রিয় ভক্তা মিজানুর রহমান।,0,religion
এদের কে জুতা দিয়ে মারা দরকার,0,religion
বাংলাদেশ সরকারের কাছে আমার একটা অনুরুধ আপনারা ব্যথ হলে আমাদের যুব সমাযের কাছে এদেরকে চেরে দেন দেখেন ওদের কেমন সাইজ করা লাগে আমরা করুম। আর আপনাকে অনেক অনেক দন্যবাদ বিডিয়টা করার জন্য,0,religion
আল্লাহ ওদের কে আপনি ‌হেদায়েত করে দেন অথোবা থনশো করে ই,0,religion
মাশাল্লা হুজুর এর বয়ান টা অনেক ভাল লাগছে সাহসি,0,religion
এমন বেয়াদব দের কারনে আজ মানুষ আলেমদের কে সম্মান করে না,0,religion
তাহলে হাজিরা মাথা কামায় কেন?,0,religion
মিজানুর রহমান আজাহারি ইনটেক্ট পরিখক। আহলেবায়তের প্রতি তার সন্মান রেখে কথা বলা উচিত।,0,religion
খুবি ছিলো,0,religion
আমার দেখা সবচাইতে ভাল ভিডিও।,0,religion
এই সালা ফাঁসি চাই,0,religion
এরে পুটিমাছ নাস্তিক,0,religion
আল্লাহ তায়ালা যে তকে কি করবে তুই সপ্নেও ভাবতে পারবি না,0,religion
আল্লা হেদায়েত করেন মানুসকে,0,religion
ভোঁদা বাগি,0,religion
আমি ও কে পেলে জুতা দিয়ে পিঠাতাম।ও হুজুর বন্ড। এ শয়তান। তার।ফতোয়া সবাই কাফির ।শুদু হে মুসলমান।আযীব এর ওয়াজ কে শুনে। এর ওয়াজ শুনলে গোমরা হয়ে যাবে। এর থেকেে দূরে থাকুন।,0,religion
তুই বহুত বড় বিয়াদব,0,religion
বলে অসীম সৌন্দর্য বোঝানো হয়েছে স্মার্ট বোঝানো হয়েছে তার মানে ওই মানুষদের যেমন রাসুলুল্লাহ সাঃ এর ও ছিলো তার মানে হলো দুনিয়ার কোনো জিনিসের সাথে রাসুলুল্লাহ সাঃ এর তুলনা করলেন আপনি কি জানেন দুনিয়ার কোনো কিছুর সাথে রাসুলুল্লাহ সাঃ এর তুলনা করা যাবে না??,0,religion
যেদিন আল্লাহর গজব আসবে সেদিন কেউ ঠেকাতে পারবে না ওদেরকে,0,religion
আসলে এভাবে আপনারা ঠেলাটেলি করেন। আমাদের কে কেন শুনান। ঢেলে দেই নিয়ে এত সন্দেহ তাকলে আপনি বলেন চরমোনাই এর জিকির কি। হুজুর এ বলবে। কথা দিলাম। আপনি জিতলে নগদে হাজার টাকা আর না দিতে পারলে হাজার।,0,religion
ওর ফাঁসি দিওয়া হোক,0,religion
তুই শয়তান তাতে আমার কোনো সন্দেহোনেই,0,religion
ওদের কপালে জুতার বারি মারি,0,religion
মূর্খ বক্তা সবাই লেগে আছে জগরা আর সে কুরান তেলয়াত শুরু করেছে,0,religion
আপনারা যারা উনাকে শিশু বক্তা বলছেন উনি কিন্তু আসলেই শিশু বক্তা না উনি একজন মাওলানা উনার বয়স এর উপরে,0,religion
আল্লাহ তুমি তাদের বিচার কর,0,religion
নাস্তিক গুলোর বিরুদ্ধে আল্লাহর কাছে বিচার রইল।,0,religion
আপনার য়ত ভিডিও দেখছি সব থেকে এই ভিডিও আমার ভালো লাখছে,0,religion
ভাই তুদের কাছে বাপের খাই আর কোন কাজ নাই খালি মানুষের দুষ খোযে বেড়াস,0,religion
তোদের ছুটাইবো খাজা বাবার লোক,0,religion
উনি আমাদের যুবকদের মাথার মুকুট উনি বাংলাদেশের একজন সেরা বক্তা উনাকে বন্ড বা কাফের বলা কোনো‌ মানেই হয়না এটা উচিত না এটা ঠিক না ।তাই সবাইকে অনুরোধ করবো কোনো কিছু না যেনে না বুঝে কাহারো বিরুদ্ধে খারাপ মন্তব্য করবেন না না না ।,0,religion
তার ভিতরে তো ঈমান নাই মানুষকে ধুকা দিয়ে জীবন চলে তার তা না হলে পেটে খাবার জুটবে না ছাগল ও ভালা তার থেকে অনেক ভালো,0,religion
আমরা শুনছি দশকের মানুষ মূর্খ ছিল বেশি এখন দেখি না তার উল্টোটা এখন তার চাইতে বেশি মূর্খ এর লোক গুলো,0,religion
অর গান কুন সালাসুনে পালতু লুক,0,religion
আমাদের ইসলামের বিরুদ্ধে কাজ করলে তোদের মত মুনাফিকদের কি করমু দেখবি,0,religion
রাইট বলছেন,0,religion
আমির হামজা ভালো তাহেরি ভন্ড,0,religion
হাফিজুর রহমান সিদ্দিকী একজন ভন্ড।,0,religion
অসংখ্য ধন্যবাদ আপনাকে ভাই আমার অনেক প্রিয় আজহারী হুজুর,0,religion
তাহেরি কে নিয়ে আলোচনা কি সেই ভন্ড মাজার পূজারী বাটপার,0,religion
অসাধারণ ভাই খুব সুন্দর হয়ে ছে এগিয়ে জান,0,religion
আমি নাউজুবিল্লাহ পড়তে পড়তে মুখে ফেনা ছুটে গেছে এই ভিডিওটি দেখতে গিয়ে। আল্লাহ ওদের হেদায়াত দান করুক। তহসিন তাই আপনিও পারলে বার নাউজুবিল্লাহ পড়ে নেন প্লিজ।,0,religion
নাস্তিকের সাথে কেন টক সো করতে গেলেন এরা ইসলামের কী ভুজবে,0,religion
সরকার এগুলো দেখেনা বিচার করেনা এই জন্য সরকারের পক্ষে জনগন নাই নাস্তিক দের ফাসি দেয়না আশ্রয় দেয় বাংলার যমিনে এদের কে মেরে ফেলা উচিত,0,religion
হায়রে কাট মোল্লারা,0,religion
কথা সুনলে মনে হয় ভন্ড,0,religion
তারার মার হেটা দেওয়ান বাগি বলেন যে আমাকে এসে কিছু করতে তার বোন্রে সুদিয়া,0,religion
ভালবাসার তাহসিন ভাই লাভ অ্যান্ড রেস্পেক্ট ফ্রম ফরিদপুর,0,religion
নাইজু বিল্লা,0,religion
এই লোকটা বললো যে গন গন মাথা কামানো আবুলাহাবের সুন্নত। তাহলে উমরা করতে হলে মাথা কামানো কি পাপ,0,religion
মিজানুর রহমান আমাদের দেশের গৌরব 💓🧡💛💚💚💙💙💜,0,religion
মাজার পুজারিরে জুতা পিটা কর,0,religion
জয় হবেরে জয় হবে হাত পাখারী জয় হবে তাইতো এবার গরিব দুঃখির নেই তো কোনো ভয়,0,religion
হে আল্লাহ তুমি এর বিচার করো,0,religion
এই চার নাস্তিক কে যারা জুতাপেটা করতে চান তারাই শুধু আমাকে লাইক করেন।কারণ আমি ওদের কে ঘৃণা করি। ওরা ইসলামের দুশমন ।ওরা কিভাবে আলেমের সাথে কথা বলতে হয় তা নিজেও জানেনা।আলেমদের সাথে বেয়াদবি মানে রাসুলের সাথে বেয়াদবি।,0,religion
আমার আইডিটা করুন।,0,religion
ভন্ড তর বাপ,0,religion
আসুন আমরা সবাই আল্লাহর পথে চলি এবং ওয়াক্ত নামাজ আদাই করি,0,religion
বাল পাকনা😡,0,religion
বক্তা সত্য কথা বলছে,0,religion
ধন্যবাদ ভাই এরকম যদি কোনো অপসোন থাকতো তাহলে আমি একাই লাইক করতাম,0,religion
আমার প্রিয় বক্তা মিজানুর রহমান আজহারি দোয়া করবেন আপনারা আমার ছেলেকে আমি হাফেজ মাওলানা বানাইতে পারি আমার ছেলের নাম হুসাইন আহমেদ আরিয়ান,0,religion
সঠিক পথের দিশা পেতে জামাত শিবিরের কোন আলেমের ওয়াজ শুনে আমার মনে হয়,0,religion
ভন্ডা মাজার পুজারী কে জুতা দিয়ে পিঠা,0,religion
বাবা খাইয়ে রোষ্ট করেন নাকি 😪😪,0,religion
এখন এই নাস্তিক গুলো বুজতে পারবে তছলিমা নাসরিন কে ভারতে জুতা মেরেছে মানুষ । বিদেশে থাকি ইহুদি খৃষ্টান রা কখন ও বলতে শুনি নি ইসলাম খারাপ ধর্ম দু খের বিষয় হল মুসলমানের ঘরে জন্ম নিয়ে হয়েছে নাস্তিক,0,religion
আলহামদুলিল্লাহ আল্লাহ আজহারী হুজুরকে অনেক ভাল রাখুন,0,religion
ওড়না নম্বরে যোগাযোগ করা যাবে কি আমার সাথে কথা বলার জন্য কথা ছিল,0,religion
আজকের হুজুররা বান্দোরের মতো রুটি ভাগ করে,0,religion
আল্লাহ আপনি এই নাস্তিকদেরকে হেদায়েত দাও আমিন।,0,religion
থাপরানোর দরকার কমিটির লোকদের কারন ও তো ফাইব পাস করেনি ও কি ভাবে মাওলানা বা মুফতি হয় কি করে সব গুলা গাজা খোর,0,religion
আমির হামজা ঠিক বোলে ছেন,0,religion
ভাই জারা এই পিরির সামনে থাকে তাদের দোস।,0,religion
নেক্সট এনায়েতুল্লাহ আব্বাসিকে করেন,0,religion
নাস্তিক জিন্দাবাদ,0,religion
তুইতো কিয়ামতের আলামত।,0,religion
আপনি ভিডিও চিত্র প্রকাশ না করে কথা বেশি বলেন,0,religion
এ মারেন মারেন মাইরা যান।।।এই সকল ভন্ডদের বাঁশ দেওয়া দরকার।।। জুতা স্যান্ডেল দিয়া পিঠানো দরকার,0,religion
ভাই হাফিজুর রহমান হুজুরকে এখানে আনাটা ঠিক হয় নাই❌,0,religion
এখন ত আমাদের দেশে এসব নাস্তিক পাইকারি পাওয়া যায়,0,religion
বি বাড়িয়ার বদনাম হচ্ছিলো,0,religion
এই লোকটা মনে হয় নিজে গাজা খায়,0,religion
কেনো মানে জানেন না আপনি আপনাদের মতো কিছু আলেম বই লিখে হাদিস বলে চালিয়ে দেয় সেই জন্য পড়ে,0,religion
আব্বাসী যদি তার কমেন্ট গুলি দেখতো তাইলে আমার মনে হয় এই সব ভন্ডামী বাদ দিয়ে জুতা সেলাই করা শিখতো,0,religion
উচিত কথার মান নাই।,0,religion
জি আলহামদুলিল্লাহ সবার ভন্ডের বিরুদ্ধে প্রতিবাদ দেখে আমিও অনেক খুশি হুজুর সত্য কথা বলছে তো তাই হেতের গায়ে লাগছে,0,religion
অাইনের বেবছতা নেয়া ইচিত,0,religion
মাজার পুজারী বেঈমানরা এখন শকতিশালী,0,religion
দুই দিনের বাচ্চা কই কি । ওর তো বালই হয়ই নাই,0,religion
ইসলাম শান্তির ধর্ম এখানে যদি বিশৃঙ্খলা সৃষ্টি করে তাহলে মাইরের উপরে কোন ওষুধ নাই,0,religion
তোর সবার সামনে অাগুনে পরানো দরকার,0,religion
ঐ নাস্তিকরা তোদের মায়ের কাছে একাধিক পুরুষ রাত কাটিয়েছে। সেজন্য তোরা ইসলাম বিরোধি কথা বলিস। তোদের জানাযা করা যাবেনা সালারা,0,religion
হুজুর আপনি ঠিক কথা বলেছেন গো,0,religion
এই ভন্ডরাই প্রকৃত ইসলাম প্রচারকারীদের বিরুদ্ধে লেগে থাকে,0,religion
হাসতে হাসতে শ্যাস,0,religion
ভাই আর ধৈর্য ধরতে পারছি না। হালারা কয় কী???,0,religion
হিজলা,0,religion
মাঝে মাঝে মনে হয় নাস্তিকদের গলাই জুতার মালা পরাই ঘুরাই,0,religion
মুগ্ধ হয়েগেলাম,0,religion
ভাই তুমি চালিয়ে যাও আমরা তোমার পক্ষে আছি,0,religion
গরুর দল গুলাও সাথে সাথে বলে আমিন🤣,0,religion
এখানে একটি চ্যানেল এর লিংক দেয়া আছে। এই চ্যানেলে এক ভন্ড নিজেকে আদম আঃ বলে দাবি করে। সেই ভন্ড দাবি করে তিনি হযরত মুহাম্মদ সঃ এর উপরে। আপনারা লিংকে দেয়া চ্যালেন ঢুকে দেখতে পারেন। সবচেয়ে বড় কথা সাধারণ মুসলমানদের পথোবষ্ট করা হচ্ছে। আসুন তার ভন্ডমী সকলের কাছে প্রকাশ করি। এবং সঠিক ইসলাম প্রচার এ সাহায্য করি।,0,religion
আপনি এক জন মহিলা। আগে আপনি পরদা পরেন। আপনার কথা হাজার হাজার মানুষ শুনতেছে এটা কি ভালো। আপনি আল্লাহর কাছে কমা চান।,0,religion
শিশু বক্তা কেয়ামতের আলামত! 😰😱 মিজানুর রহমান আজহারী,0,religion
হে আল্লাহ এ নাস্তাকির উপর গজব নাজিল করেন।,0,religion
ওরা নাস্তিক নয়। ওরা মুসলিমই শুধু হেফাজত কওমি জামাতিদের ইসলাম ধর্মের অপব্যবহার শাপলা চত্ত্বরে কোরআন পোড়ানো সহ নানা প্রশ্ন করেছেন। আর ওই নামধারী ভন্ড মৌলভী মূর্খের পরিচয় দিয়েছে।,0,religion
আমার অনুরোধ কোনো আলেম ওলামা যেনো টিভি তে টকশো না করে,0,religion
হুজুর কথা টিক আছে ভন্ডরা এরকম করে,0,religion
বর্তমান তথ্য প্রযুক্তি ও বিজ্ঞানের যুগে নাস্তিকরা হলো সবচেয়ে হাস্যকর প্রাণী,0,religion
আসালালম ও আলাইকুম আমি ভারত থেকে মিজানুর রহমান আজহারি সাহেব খুব ভালো মনের মানুষ এবং যুবক ও বৃদ্ধা সকলের খুব ভালো ভাবে বোঝাতে পারেন। আল্লাহ উনাকে এবং উনার পরিবারকে এই ভাবে নেক হায়াতের সাথে চলার তৌফিক দান করুক।,0,religion
ভাই তোমার সাথে আমি একমত এরা সব শয়তান ভন্ড,0,religion
আপু আপনাকে ধন্যবাদ বন্ড পিরের বিরুদ্ধে থাকার জন্য !,0,religion
আজহারি একটা বিয়াদব তার বক্তরা মুর্ক,0,religion
বেয়াদবের মত কথা বলা একটুক পুলাপান আংগুল উছা করে কথা বলে আবার ইস্লামিক কথা না বলে অই ফিত্না করে জত গেনি মানুশ হক না কেন বাংলা পুলাপান তো পুলাপানি বাশের চেয়ে কঞ্চি বর হয়ে গেছে বরত্মানে,0,religion
গাধা মোল্লা,0,religion
সবচায়তে বড় বন্ড দেওয়ানভাগী হারামি বাকিরা,0,religion
সড়যন্ত মূলক টকশ। মুরগি,0,religion
বাংলাদেশ। সব চেয়ে ভড় হুছর হলো আমাদের মিজানুর রহমান।,0,religion
যারা কমেন্ট গালা গালি কর্রা তারা তানর মত যুগ্যব্যাক্তি হন তানর বয়স হয় তাহলে শিশু হন কিবাভে??? গাদার দল,0,religion
ন্যাড়া হওয়া সুন্নত এইটা কইলি না বেটা ভন্ড,0,religion
তরে জদি আমি পাইতাম কতদিনে কত চাল শালা বেয়াদব। তোর জন্মমের ঠিক নাই। গিবত আর গিবত,0,religion
আগে বানান সিক তার পেরে পতিবাদ করো ওকে,0,religion
মামুনুর হক আপনি আপনার বতব্য চালিয়ে যান নাচতিক দের বলে যায় ইসলামের বিরিদিতা করলে পিঠের থাকবেনা সে এমপি হোক তার গডপাদার হোকনা কেন আমাদের ডাকবেন,0,religion
বাঙালি কে জাগিয়ে তুলতে শিক্ষিত সমাজে অশিক্ষিত মানুষকে চোঁখ খোলে দিতে আমাদের কে ভরতে দিন চেয়ার নড়াচড়া করে একটু হলুদ একটু মরিচ দিয়ে বানিয়ে সমাজকে দূষণ মুক্ত ও শোষন মুক্ত করার জন্য আশোন আমরা নেমে পড়ি।ঈদ মোবারক সবাইকে।,0,religion
মজা,0,religion
ভন্ড তাহেরিকে জুতামার,0,religion
নাস্তিকের দল। যাদের ইসলাম সম্পর্কে জ্ঞান নেই তাদের সাথে কথা বলে কোন লাভ নেই। এরাই হল ইয়াহুদী খ্রিষ্টান এর দালাল।,0,religion
মিজানুর রহমান আজহারি আমার প্রিয়ো একজন ভক্তা,0,religion
ওয়াজ নামের কলঙ্ক!! জিকির কে অসম্মান করতাছে পাপী!! বেয়াদব! হুজুর নামের কলঙ্ক! এদের জন্যই দুনিয়া আজ ধ্বংসের পথে জিকিরের নামে গান হচ্ছে,0,religion
ভাই ভইরা দিছেন এক্কেবারে! 😂😂,0,religion
আল্লাহই জিব্রাইল এটা তো কোরআনের আয়াতেই প্রমাণ করা যায়। ইসলামিক স্কলারদের বক্তব্যই তো ওটা। জিব্রাইল,0,religion
হে আল্লাহ আমাদেরকে রক্ষা করে,0,religion
প্রিয় হুজুরকে হাজার সালাম,0,religion
আল্লাহ আপনি নাস্তিক দের হেদায়েত দান করুন,0,religion
হযরত এখলাসের সাথে এগিয়ে যান আল্লাহ আপনি সহায় হোন,0,religion
আপনার সাহসিকতাকে স্যালুট,0,religion
তোকে ডিম থেরাপি দেওয়া দরকার,0,religion
আল্লাহ তাদের জাহান্নামের সবচেয়ে কঠিন শাস্তি দিবেন,0,religion
হেরে ওয়াজে নেয় কোন লোক শয়তান,0,religion
আপনাদেরকে অনেক অনেক দন্যবাদ,0,religion
একটি বিষয় বুঝিনা এই ভন্ডগুলো এভাবে ইসলামের অপপঅপপ্রচার করে প্রিয় নবীজী তাঁর কন্যাকে এতো খারাপ কথা বলে এতো ভন্ডামি এসব অমানুষ শয়তানদের সরকার কেন গ্রেফতার করে আইনের আওতায় আনেনা!!,0,religion
লোডা লিকের আমলে যা হয়,0,religion
ধন্যবাদ ভাই আপনাদের,0,religion
কেকে মিজানুর রহমান কে ভালোবাসো আমার এই কমেন্ট এ লাইক দাও,0,religion
আসলে আমরা বাঙালিরাই সব থেকে বড়ো মূর্খ আচ্ছা কুরান ও হাদিশ আমাদের সবার জন্য তাহলে কেনো আমরা সেটা পরে সত্য মিথ্যার বিচার করি না ? কেনো হুজুর দের ওপরে সবাই ভরসা করে ? আমরা কুরান ও সহীহ হাদিশ পরেই তো সত্য মিথ্যার যাচাই করে চলতে পারি আ,0,religion
এই লুগ গুলো রে উছিত শিক্ষা দেওয়া হক,0,religion
জন নাস্তিকের কবরের যে কি হবে একমাত্র আল্লাহ পাকই জানেন,0,religion
গাধা মুয়াজ্জেম যা বলবে তাই কেন বলবে।ভন্ড মানুষের মধ্যে ফেতনা ছরাচ্ছে।ভাল হ সময় এখনও আছে।মরতে হবে।নাকি মরবি না।বোকা মুর্খ,0,religion
এয় নাছতিকের বাচা চোপ কর,0,religion
বছরের বাচ্চা ও জানে দেওয়ান বাগী ভন্ড।আমাদের মুসলিম হিসাবে দায়িত্ব সবাই মিলে এটাকে মেরে ফেলা। এতো ইসলামিক দল থাকতে । এতো হুজুর ক্যান এর বিরুদ্ধে যুদ্ধ করে না।,0,religion
আবার ও জুতা পিটা করা হবে,0,religion
💐💐কে কে 👰আমার মতো সত্যকে ভালোবাসেন।লাইক দিয়ে যান।💐💐,0,religion
ভাই এইসব দেখলে নিজের উপর গিনা হয় কেন আমরা দুনিয়াতে বেচে আছি কি জবাব দিব আল্লাহর দরবারে আমরা আল্লাহ পাক আমাদের সবাইকে রহমত করুক আমিন,0,religion
বাতিলকে মঞ্চ থেকে ঘাড় ধরে বের করে দেওয়া ঠিক হয়েছে,0,religion
আইএস এরে দেখে না!!!😑,0,religion
আব্বাছি ভন্ড,0,religion
তাহেরির গালে জুতা,0,religion
এর কপালে ওনেক খারাপ আচে,0,religion
হের জন্য আমাদের ব্রাহ্মণবাড়িয়ার মানুষের মানসম্মান রইলো না।,0,religion
এইসব ভন্ড দের ধরে ধরে মারা উচিত,0,religion
ধন্যবাদ হুজুর কে। হক কথা বলার জন্য। আল্লাহ সবাইকে সঠিক পথে চলার তাওফিক দাও।আমিন।,0,religion
খেলা হবে,0,religion
আরে কাকে বাল বলব,0,religion
গুড ছোট ভাইয়েরা,0,religion
তাহেরি কে ওয়াজ করা থেকে বিরতো রাকা হোক ও আসলে ভন্ড,0,religion
ইসলামকে নিয়ে মজা করা ঠিক নয় এটা কাফিরদের কাজ।,0,religion
আললাহ এদেরকে হায়াত দান করুন আমিন,0,religion
আসালামু আলাইকুম ভাইজান আপনার মাথাই টুপি কুথাই টুপিদিলে আরো ভালো লাগতু।,0,religion
হায়রে মানুষ হইলি বেহুশ দম ফুরাইলে ফুস। তবু কেন হয়নি তোমাদের একটু খানি হুশ।,0,religion
এই জানোয়ার এখানে দুজনই সঠিক কথা বলছেন তুই উল্টা পাল্টা কথা বলতেছো কেনো?,0,religion
মালাউন,0,religion
হে আল্লাহ তাদেরকে এমন শাস্তি দেন তারা যেন জাহান্নামেও জায়গা না হোক,0,religion
সবথেকে ভন্ড আব্বাসি আর তাহেরি,0,religion
ছোট বয়স থেকেই গীবত শিখতেছে এরাই আসল ভন্ড,0,religion
আবাল দিয়ে দেশ ভরে গেছে রে ভাই।,0,religion
সত্য শান্তির জন্য নয় হারাম কামাবার জন্য এই,0,religion
তাদের উপর যেন খুব তারাতারি গজব নাজিল হয়,0,religion
মাশা আল্লাহ।,0,religion
এদের কে জুতা মারা উচিত,0,religion
জন নাস্তিক,0,religion
থ্যাংক ইউ সো মাচ ভাইয়া আপনাকে ভিডিওটা বানানোর জন্য অনেক ধন্যবাদ,0,religion
এই সমস্ত হুজুরের ধান্দা হলো পয়সা কামানো এরা ধর্ম সম্পর্কে কিছুই জানেন না ।,0,religion
হুজুর ওনেক প্রমান আছে আল্লাহর অলি দের পাওয়ার আছে,0,religion
অজুর আপনি ঠিক বলছেন তাহেরির মত বন্ড কে নিয়ে আপনার সময় নস্ট কইরেন না আপনার থেকে আমাদের অনেক কিছু শিখার আছে দুয়া করবেন ❤,0,religion
আললাহ শয়তান থেকে আমাদের কে হেফাজত করেন,0,religion
ভন্ড তাহেরী তোর চেহারায় দেখা যায় তুই শালা বড় ভন্ড ।,0,religion
এডমিন এ গুলো ভালো না,0,religion
এরা কেউ নাস্তিক নয়। এরা মুলত ইসলাম বিদ্বেষী। অতএব এদের সঙ্গে প্রখর জ্ঞানী ব্যক্তি দ্বারা লড়াই করতে হবে। তারপরও যদি মেনে না নেই তবে বুঝতে হবে এরা তারা যাদের কোন বিবেক চেতনা নেই। আছে শুধু অপকর্মের নেশা। আর অপকর্মে আসক্ত মানুষেরা সর্বদায় ইসলামের বিপক্ষে। যতক্ষণ না আল্ল হ তাদের হেদায়েত দান করেন।,0,religion
তুই যে হাদিস জানিস না যা বললি সব ভুল ভাল হাদিস দিচ্ছিস,0,religion
দেওয়ানবাগি ওর কথা কি আর বলব।ও শয়তানের চেয়েও খারা শয়তান।বেয়াদব।,0,religion
এখন অনেকে বলবে ধুরর সব মুল্লা খারাপ এই বলে অনেকে সব মোল্লা এরাইয়া চলবে এই বিষয়ে একটা ভিডিও চাই,0,religion
ভন্ড দেওয়ানবাগির পেট পাঠাবো।,0,religion
আল্লাহ আমাদেরকে হেদায়ত,0,religion
এই চশমাওলা বেয়াকুব কোরআন বিশ্বাশ কর হাদিস বিশ্বাশ করনা কেন,0,religion
দেওয়ান বাগি তরে পাইলে হত্যা করবো,0,religion
তাদের সকলেরই একবারে প্রশ্ন অাছে,0,religion
এই শয়তানটারে একবার যদি আমার সামনে পাইতাম রে,0,religion
এ বক্তা পাগল হয়ে ছে,0,religion
হুজুর ভালো কথা বলছে,0,religion
নাস্তিকদের জন্য রয়েছে ধারালো চা পাতি ব্লাগার রাজিব বুঝতে পারছে চা পাতি কাকে বলে চা পাতি ধার করে রাখ ধার করে রাখ ঘরে ঘরে নাস্তিক মুরতাদ সাবধান কথা হবে চা পাতির ভাষায় ইনশাঅাল্লাহ্☝,0,religion
সম্রাট য় তালা খুললেন। আবার রেশমি কাপড়। এবারের ছবিতে চেহারা শুভ্র লালচে চোখ বড় মাথা “চেন এঁকে?” “না।” “ইনি নুহ  আ ।” য় চেম্বার খুললেন। এবার রেশমি কাপড় সরাতেই যে ছবি দেখলাম সেখানে শুভ্র ত্বক সুডৌল দেহ উজ্জ্বল কপাল কারুকার্যময় গাল সাদা দাঁড়ি যেন তিনি জীবিত হাস্যরত। “চেন?” “না।” “ইনি ইব্রাহিম  আ ।” এরপর আরও একটি তালা খুললেন ছবি বের করতেই চিনে ফেললাম ইনি মুহাম্মাদ স । আমাদের কান্না চলে এলো। আমরা সম্মানে দাঁড়িয়ে গেলাম। সম্রাট বললেন “আল্লাহর কসম সত্যি করে বল ইনি তোমাদের নবী?” “হ্যাঁ ইনিই। কিন্তু ইনি আর আমাদের মাঝে নেই।” সম্রাট কিছুক্ষণ আমাদের দিকে তাকিয়ে রইলেন।  এরপর বললেন “এটা ছিল সিন্দুকের সর্বশেষচেম্বার। এর আগে আরও অনেক চেম্বার ছিল। তোমরা কী বল সেটা দেখার জন্য তড়িঘড়ি করে এটা আগে দেখিয়েছি।” এরপর তিনি আগের তালাটি খুললেন এতে আগের মতো আরেকটি ছবি ছিল। এবারের ছবিটি যুবক বয়সের কারও। তাঁর চেহারায় সাধুতার চিহ্ন স্পষ্ট। সুশ্রী চেহারা। কুচকুচে কালো দাঁড়ি। অনেক চুল। সম্রাট বললেন “এঁকে চিন?” “না।” “ইনি ঈসা  আ ।” তিনি আরও কিছু তালা খুলে দেখালেন একটাতে দেখা গেল ট্যান চামড়ার বেশ কোঁকড়া চুলের আর অন্তর্ভেদী দৃষ্টির এক লোক। জানলাম ইনি মুসা  আ । তাঁর পাশের ছবিতে প্রশস্ত কপাল অইলি চুল আর হালকা টেড়া চোখ এর একজন। জানলাম ইনি হারুন  আ । এরপর একজন গড় উচ্চতার সোজা চুলের মানুষ তিনি ছিলেন লুত  আ । তাঁর পাশে প্রায় মুসার মতই দেখতে তবে লালচে ত্বক উঁচু নাক চাপা গালের একজন সুদর্শন লোক। তিনি নাকি ইসহাক  আ । এরপরের ছবিতে দেখলাম প্রায় হুবহু দেখতে ইসহাকের মতো একজন কেবল ঠোঁটের উপর একটা তিল। ইনি ইয়াকুব  আ । তাঁর পাশে হাস্যজ্জল লালচে সুদর্শন একজন ছিলেন তিনি ইসমাইল  আ । দেখতে যেন আদর্শ পুরুষ। এরপরের জন দেখতে আদমের মতই কিন্তু এত এত্ত সুন্দর যেন সূর্য জ্বলজ্বল করছে। জানলাম ইনিই ইউসুফ  আ । এর পরের ছবিতে দেখা গেল সরু পা ছোট চোখ কিন্তু বড় পেট। লালচে ত্বক। গড় উচ্চতা। তিনি ছিলেন দাউদ  আ । তারপর একজন লম্বা অশ্বারোহীর ছবি দেখলাম। হেরাক্লিয়াস বললেন ইনি সুলাইমান  আ ।,0,religion
মিজানুর রহমান কে অনেক ধন্যবাদ আমাদের সবার পক্ষ থেকে,0,religion
চার জন বড়ো গেনি ওদের জনগনের কাছে পাঠানো হক,0,religion
কথায় কথায় কয়েকটা ইংরেজি বলে নিজেকে শিক্ষিত প্রমান করার নাম ইসলাম না।,0,religion
ক্ষমতায় গেলে এই দেওয়ানবাগী কে পাছায় বাড়ি দিয়ে নাচানো হবে। ইনশাআল্লাহ!!! আমাকে ভোট দিয়েন প্লিজ 🤣,0,religion
ওরে চা খাওয়ান সব ঠিক হয়ে যাবে??,0,religion
দাড়ি রাখলে যে ভালো হয় সেটা আশলেই ভুল,0,religion
সবগুলা এক নাম্বারের,0,religion
আমি এই নাস্তিকের ফাশিচাই,0,religion
এদের সবকটাকে দূরে চোখ দুটো তুলে দেওয়া উচিত তাহলে বুঝতে পারত,0,religion
আড়ালে উনি কাঁচা মাংস বিক্রেতা।,0,religion
মিজানুর রহমান আজহারী হুজুরের সঙ্গে কোনো তুলনা হয় না|❤ ভন্ড তাহেরী নিজেকে মিজানুর রহমান আজহারী হুজুরের সঙ্গে তুলনা করেছে😡,0,religion
যেখানে হযরত মোহাম্মদ সঃ বাদে সব নবী রাসুল এবং সমস্ত উম্মাত গন বলবে ইয়া নফসি ইয়া নফসি সেখানে তর বাবায় কি করবে রে পাগল,0,religion
হালারা আসলেই গাজা খায় এরা আসলে মানুষ নাকি এলিয়েন 😂 আমি আর হাসতে পারিনা ভাই 😂😂😂 হাসতে হাসতে পেটে ব্যাথা শুরু হইছে আমার হালাগো লজিক শুইনা।😂😂😂😂,0,religion
তুই আলেমের কি বুঝিস,0,religion
যারা পাসে ভসে আচে সব নাস্থিকের দল।,0,religion
যেই হাজার ভন্ড আনলাইক দিসে ওরা দেওয়ান বাগীর ভক্ত,0,religion
তুমার মাথার টুপি কই,0,religion
আব্বাসির চেহেরা বিয়াদ্দফ,0,religion
আজহারী সাহেবের জুতার সমান ওনা,0,religion
সেলুট লোপা,0,religion
এক ভন্ড পীর যে দেশে বসেই নকল ক্বাবা বানিয়ে হজ্জ্ব করার নিদারুন পথ তৈরি করেছিল তার ব্যাপারে কিছু বললেন না?,0,religion
আল্লাহ হেদায়েতে মালিক আল্লাহ আপনাদের সকলকে হেদায়াত করুক আমিন।,0,religion
মাদারবোর্ড তুমি বড়ই ফেতনাবাজ,0,religion
আজ রোস্টিংটা দেখতে ইচ্ছেই করলো না বিরক্তিকর লাগছিলো এই ভন্ডকে সহ্যই হচ্ছিলো না পুরা ভিডিওটা দেখতে পারলাম না,0,religion
আল্লাহ ওদের বিচার করুন,0,religion
এরা সব ভন্ড শয়তান,0,religion
নাস্তিক টা একসাথে আল্লাহ তোদের বিচার করবে আর তোরা এই হজুরকে প্রশ্ন করতেসিস আর হজুর এর উত্তর আসবে আল্লাহর পক্ষথেকে,0,religion
এগিয়ে যান ভাই সাথে আছি,0,religion
আল্লা তুমি এদের বিচার করবে,0,religion
এরা।আলেম।না।যালেম।হাইরে।মানুষ আফসুস।তোমাদের।প্রতি।এই।ভন্ডরা।যে।শিরিকি।কুফুরি।কিচ্ছা কাহিনি।বইয়ান।করে।তা।কুরআন।হাদিছ।দিয়া।জাছাই।করলানা।এই।ইসলাম বিরুদি।কথা।কি।কুরআন।হাদিছে।আছে।না।ভন্ড।পিরেরা।এই।শিরিকি।কুফুরি।কথা।নিজেরা বানাইছে।তুমরা।আফসুস।করবা।কিয়ামতের।মাঠে।হাই।কি।করলাম দুনিয়াতে।তখন।আর।তোমাদের।আফসুস।কুনু।কাজে।আসবেনা,0,religion
মামুনুল ভাই,0,religion
ভাই এগিয়ে যান আমি পাশে আছি আমরা সব ভন্ডামী উড়িয়ে দেব,0,religion
ভাই বেয়াদব দের ভিডিও আপলোগ কেনো করেন আপনি খুব ভালো না ভাই,0,religion
মানুষ ভুল পথে যায়তেছে আল্লাহ তাদেরকে হেদায়ত করুন।,0,religion
হযরত রাসূল সাল্লাল্লাহু আলাইহি ওয়াসাল্লাম কে কিভাবে আমল করে স্বপ্নে বা মোরাকাবায় দেখতে পারবে সেই শিক্ষা দিয়ে যাচ্ছেন হযরত দেওয়ানবাগী হুজুর আর তোমরা তার বিরোধিতা করতেছ তাই না,0,religion
টা ছাগল,0,religion
এই সব গুলো ভন্ডদের কারণে মুসলিম উম্মাহ আজ পথভ্রষ্ট বিপথগামী হাদিস কোরআনের সাধারণ জ্ঞান টুকু এদের মধ্যে নেই কিচ্ছা কাহিনী বলে ওয়াজ মাহফিল করে আর মানুষ না বুঝেই বাহ্ বাহ্ দেয়,0,religion
হে আল্লাহ তাদের থেকে আমাদের হেফাজত করুন,0,religion
তাহেরির মতো জানুয়ারের ও ভক্ত আছে আর সেই ভক্তের কি নাম দেয়া যায়,0,religion
আজহারী খারাব,0,religion
হাফিজুর রহমান একজন আলেম আপনারা মুসলমান দের মাঝে সমস্যা লাগানোর জন্য এসব লিখা আর লেখবেন না,0,religion
এদের বলে মুসলিম ভাই হুজুর কে আমার সালাম,0,religion
তাহেরি সাহেব আপনি কোনপীরসাহেবের কাছথেকে খেলাপত নিয়েছেন আমি প্রায় দেখি আপনি বোলেথাকেন আপনার দরবারের কথা তারমানেকি আপনি নিজেকে পির দাবিকরেন।জোদী আপনি নিজেকে পিরদাবিকরেথাকেন তাহলে আমিবলব আমি আপনার মাজে পিরের কোনো কিচুইদেখিনা। আপনি শুদুই একজন বক্তা,0,religion
এর মতো ভন্ডর ফাসি চায়,0,religion
কেয়ামতের আলামত,0,religion
শান্তির ধর্ম,0,religion
নাস্তিকরা নিজেদের খুব জ্ঞানী মনে করে কিন্তু বাস্তবে তারা জ্ঞানশূন্য । উপস্থাপকসহ বাকীসব অতিথিরা যেভাবে আক্রমণাত্বকভাবে হুজুরের সাথে কথা বলতেছে মনে হচ্ছে হাজার বছর ধরে শত্রুতা রয়েছে।শাহরিয়ার কবির সম্পর্কে সবাই জানে যে সে একজন আপাদমস্তক ইসলাম বিদ্বেষী। হাজার হলেও উপস্থাপকের উচিৎ ছিল তার ইসলাম বিদ্বেষী মনোভাব প্রকাশ না করে সকল অতিথিদের প্রাপ্য সম্মানটুকু দেওয়া।,0,religion
তিনটা ছাগল কি বলে! মুরগী চোরটা ইসলাম সম্বন্ধে কিছু জানেই না। জানলে এত বড় গোঁফ রাখতেন না। মডেল তো দুইটা কোরআন ও সুন্নাহ।,0,religion
বুঝতে পারছি এনায়েতুল্লাহ আব্বাসী ধৈয্যশীল নয়। তার মাথা গরম এমন মানুষ আবার কি করে পীর হয়? আমার জানা নাই। ব্যবহার ও চরিত্র উত্তম এই নয় যে মানুষের পাছাই আঙ্গুল দিয়ে নিজে ভাল থাকা।,0,religion
আমি এই চার নাস্তিকদের বলতে চাই আবুজাহেল কোথায় বাস করত,0,religion
নামাজ নামাজ নামাজ পড়েন সবাই মিলে পাঁচ ্্্্্্,0,religion
এই সব ভন্ড মাজার পূজারী দের কে জুতা পিঠা করে দেশ থেকে তাড়ানো উচিৎ।,0,religion
তাহেরিরে তাহিরি তাহেরিকে,0,religion
গজব দিবেন আল্লাহ,0,religion
সূফী সম্রাট দেওয়ানবাগী হুজুরের শিক্ষা নিয়ে আলোচনা জানতে হলে দেখুন,0,religion
মিজানুর রহমান,0,religion
খুব সুন্দর কথা বলছেন ভাইয়া,0,religion
এটা তো পুরোই পাগল,0,religion
চাইটা বেঈমান একটা ঈমানদার,0,religion
ভাইয়া♦♥,0,religion
ভাই ওকে রাসতায় সবার সামনে ঊলুঙ করে ফাঁসি দিতে হবেই,0,religion
জাতীয় আবালদের সাথে পেচাল পেরে লাভ নাই হুজুর।,0,religion
হালারা জানে না যে ইসলাম প্রতিশোধ নেওয়ারর জন্য না শান্তির জন্য।,0,religion
সালা তুই তো নাজায়েজ বক্তা হারামি,0,religion
বাচ্চা তুই সাহস বড় রে তুই এখন ই একজনের গিবত করস মনে রাখিস আল্লাহ তায়ালা তকে ছারবেনা,0,religion
ভন্ড নবী ও ছিল হুজুর এ পাক এর আমলে। তো ভন্ড পীর কেমনে থাকবেনা । তবে কোন যায়গা সম্পর্কে না জেনে কোন সত্য পীরেরনামে যদি কুকথা বলে তাও ভন্ডামী ও এক ধরণের গীবত ।,0,religion
গীবত কি গীবত কাকে বলে গীবত কখন জায়েজ গীবত সম্পর্কিত হাদিস গীবতের শাস্তি। বিস্তারিত পড়ুন,0,religion
আমরা যদি নফসের তাড়নায় পাপের কাজ না করি তাহলে রুহ পবিত্র থাকে। আমরা যখন নফসের দ্বারা এবাদত বন্দেগী করি তখন এই এবাদত বন্দেগীর প্রতিফলন গিয়ে রূহের উপরে গড়ায় রূহের উপরে পরে রুহ আরো শক্তিশালী হয় । সূফী সম্রাট হযরত শাহ্ দেওয়ানবাগী মা আ,0,religion
কোন দুনিয়ায় বাস কোরে এই পাগলগুলা। এর সময় এমন মানুষ দেখি নাই।,0,religion
জি আলহামদুলিল্লাহ সবার ভন্ডের বিরুদ্ধে প্রতিবাদ দেখে আমিও অনেক খুশি,0,religion
কেয়ামত অতি নিকটবর্তী 😭😭,0,religion
এ শিশু না বামন বছর বয়স হবে।,0,religion
আল্লাহ তাদের হেদায়ত করুক।,0,religion
বন্ধ করুন সবার মন্তব্য ফুল ভিডিও না দেখে উল্টাপাল্টা মন্তব্য করবেন না! শেষের দিকে মিনিট সেকেন্ড যখন আব্বাসিকে পীর সাহেব নিয়ে প্রশ্ন করা হয়েছিল তখন পিছন থেকে হয়তো সে পীর অথবা পীরের মুরিদ কথা বলে ওঠে যে এত প্রশ্ন করা ঠিক না তখন আব্বাসী বলে ওঠেন যে আপনাদের লোকই তো প্রশ্ন করছে তখন সে পেছনে থাকা লোকটি বলে উঠেন এ বিষয়টি আমি দেখছি বলে দাঁড়িয়ে কথা বলতে শুরু করেন এরপরে সামনে সবাই যখন উল্টাপাল্টা কথা শুরু করে তখন আব্বাসী রাগ করে চলে যান হয়তো আমি লিখে বুঝাতে পারলাম না বোঝার জন্য ভাল করে ভিডিওটি দুচারবার দেখতে থাকুন বুঝে যাবেন এই ভিডিওটি ভাইরাল হওয়ার জন্য এরকম কিছু লেখা হয়নি পীর সাহেব সম্পর্কে ধারণা দেওয়ার জন্য লেখা হয়েছে যেন সবাই ভিডিওটা দেখে এবং পীর সাহেব সম্পর্কে ধারণা পায় ধন্যবাদ ভালো থাকবেন সবাই,0,religion
যাগ মুসলমান,0,religion
অনেক ধন্যবাদ। এরকম আরও ভিডিও বানালে ভাল হবে।,0,religion
আল্লাহর কাছে প্রার্থনা করি দেওয়ার বাগির জনো ফেরাউন চেও আজাব দিক সাথে চেলাবেলাও,0,religion
এমন জিবন গরিব গঠন মরিলে হাসিবে তুমি খাদিবে ভুবন,0,religion
হিচানি মহিলা উপসতাপিকা। সুকরের মত লাগে। জংগল।,0,religion
এই সব মাওলানা কে মারা উচিত কেন না তুই নিজের কথা ক না হলে পরে কথা ধরে টানিশ কেনো যতো সব ঝগড়া লাগা মাওলানা,0,religion
আপনি দেওয়ানবাগী আর আতিকুল্লা এইসব ভন্ডদের সাথে এনায়েতুল্লাহ কে কিভাবে মিলালেন!!আর যাই হোক উনি ওদের কাতারে পড়েন না!,0,religion
তর কপালে জুতা,0,religion
আমির হামজা একটা আবু জাহেলের ছোট ভাই,0,religion
খালি বাবা দের নাম নেয় এরে দেখলেই জুতা মারতে চান কে কে ??,0,religion
দোয়া করি তোদের অপর আল্লাহ যেনো হেদায়েত করোক তানাহলে তোদের অপর গজব পরোক,0,religion
রাইট ভাই ভাল করেছে,0,religion
ভন্ড পীর জুতা মারা হোক,0,religion
এই ছেলেটা মনে হয় সিগারেট খায় তার ঠোঁট দেখে বোঝাযায়,0,religion
ইসলামে কোথাও নাই মানুষ নিয়ে সমআলোনা করা এসব বক্তার কথা শুনলে জাহান্নাম অনিবার্য,0,religion
এই ভন্ড কে বাংলাদেশ থেকে নিশিদ্ব করা হোক,0,religion
আসসালামুয়ালাইকুম ইমান যদি ধরে রাখতে চাও তাহলে অন্যের সমালোচনা না করে নিজের সমালোচনা করো। আল্লাহ খুশি হবে। ভুল বললে ক্ষমার দৃষ্টিতে দেখবেন।🙏,0,religion
দেওয়ান বাগি পির নয়।। পিরিয়ড 😂😂😂,0,religion
সব ই ভালো লাগলো কিন্তু অই লোক এর কথা টা সত্ত ছিল। হজরত শাহজালাল রহঃ এর মাজারের আশেপাশে পুলিশ চেক থাকে সেই খানে আসলেই গাজা খাওয়া হয়না। এমন কি মাজারে দারিয়ে জিয়ারত করতে বলে মাজার কমিটি। এছাড়াও কন নংরা কোন পাগল কেউ ঢুকতে দেওয়া হয় না।।,0,religion
টিভি চ্যানেলটি হলো নাস্তিক এর খনি,0,religion
এতো হুজুর নয় মাইকেল জ‍্যকসন,0,religion
সবার উদ্দেশ্য করে বলছি যারা ভুলভাল ভাবছেন ভাই হুজুর দেখতে ছোট তাই বলে শিশু বক্তা নয় উনি হাফেজ এবং আলেম উনার সনদ এর ভিডিওটি আমি নিজে দেখেছি।হাজার হাজার আলেমের সামনে অই সনদ এর দিন উনি বক্তব্য দিয়েছিলেন আমার ইউটিউব হিস্টুরিতে এখন সেই ভিডিও টি আছে।,0,religion
ঠ্যাটা পড়ে না কেন ??? আল্লাহর গজব পরব ভন্ডবাগী,0,religion
সে মারাত্মক মিথ্যা বলেছে বিশ্ব নবী সাঃ তিন প্রকারে চুল রেখেছেন লিম্মা ওয়াফরা দুম্বা অর্থাৎ কান বাবরি কান ও কাঁধের মধ্যবর্তী ঘাড়ের শেষ চূড়া অর্থাৎ শাহারা রগ বা মাথাটা যে রগের ওপর দাঁড়িয়ে অাছে সে পর্যন্ত৷তার বেশি তিনি রাখেন নি ঘাড় ছাড়িয়ে বা কাঁধ অব্ধি রাখেন নি বরং নিষেধ করেছেন বলেছেন মেয়েদের সাদৃশ্যে চুল রাখলে অাল্লাহ পাকের লা নত রাসূল সাঃ এর লা নত ফেরেশ্তাদের লা নত অাপনারা কষ্ট করে শামায়েলে তিরমিযি শরীফটা পড়ে নিবেন তাহলে ক্লিয়ার কনসেফ্ট পেয়ে যাবেন অারমাথা ন্যাড়া করা সুন্নাতে সাহাবী রা হযরত অালী রাঃ বার বার মাথা ন্যাড়া করতেন যদিও একটা কারনে তারপরও মাথা ন্যাড়া করা হারাম কোন বিষয় নয় অারেকটি কথা সে যেভাবে ভাষা ব্যাবহার করেছে রাগারাগি করেছে অশ্লীল বাক্য প্রয়োগ করেছে কিছু দলের নাম বলে তিরস্কার করেছে অাহলে হাদীসদেরকে অাহলে খবিস বলে উল্যেখ করে যেভাবে অহংকার করে বক্তব্য প্রদান করেছে তা শুধু মাত্র ইবলিশের সাথে মিল খুঁজে পাওয়া যায় অাল্লাহ অামাদের সবাইকে মাফ করুন অামীন,0,religion
তাহেরি একটা পাগল,0,religion
তুইত এমনেতেই ভন্ড মাজার পূজারি,0,religion
ইসলাম যদি গালি দেওয়া শিখাইতো তাহলে মাজার পুজারিদের মন ভরে গালি দিতা‌ম। ইসলাম আমাকে দেওয়া করা শিখাইছে । তাই সকলের জন্নো দোওয়া করি । আল্লাহ্ তায়ালা সবাইকে হেদায়েত করুন আমিন সুম্মা আমিন ।,0,religion
ভাই সত্যি দেখার তোমাকে জানাই এবং সবস্ক্রাইব নোটিফিকেশন করলাম,0,religion
ওরে আইনের মাধ্যমে নয় আমি সামনে পেলে ভুমবাই মরি দিয়ে করা রোদে হাত পা চারদিকে টানা বান দিয়ে রেখে দিতাম তাহলে বুজতো কুরআন ও ইসলাম ও মহান আল্লাহর নামে এসব বলা কতো অমানবিক আল্লাহ কেন তার ওপর গজব নাজিল করে আমরা তার বান্দা হইয়ে সইতে পারি না আল্লাহ কাছে কেমন লাগে জার দইয়ায় এই পৃথিবিতে আসা আর তারে অপমান আল্লাহ তোমার কাছে আকুল আবেদন রোজহাশরের মাঠে তাকে কঠিন থেকে কঠিনতম শাস্তি দিবা আসুন মুসলিম ভাইবোনরা আরো একটিভ হই এসবো নাস্তিকদের আমাদের বাংলার বুক থেকে ধংশ করে দেই প্রয়োজনে জীবন দিবো তবু মহান আল্লাহর নেমে অপমান সয্য করো না ওপরে একটু খারাপ বিহেপ করে বন্ধুরা মনে কিছু করবেন প্লিজ ভূলকিছু বলে থাকলে খমার দৃষ্টিতে দেখবেন আসলে মহান আল্লাহর ও সঃ নামে কিছু শুনলে মাথা ঠিকরাখতে পারি না?,0,religion
স্যালায় শুধু ভন্ড নয় স্যালায় একটা বিশ্ব চিটার একটা বিদাত পন্থি কুলাঙ্গার ওর মুখে প্রশাব করা হউক ওকে এরেস্ট করে কারাগারে পাঠানো হউক । সাইদ কামাল মালোশিয়া,0,religion
হেফাজতিদের কি ব্রেন হা হা হা তা আবার জাকিরের বিরুদ্ধুতা করে।,0,religion
আল্লাহ সবাইকে ভালো মন্দ বুঝার ক্ষমতা দান করুন ভন্ড সালাদের জদি ক্রস ফায়ার করে মারতে পারতাম খুব খুশি হতাম,0,religion
মিজানুর রহমান আজহারী হজুর আমাদের অহংকার,0,religion
টিভি চ্যানেল গুলোতে কয়েকজন নাস্তিক মুরতাদদের সামনে একজন আলেম কে ডেকে নিয়ে এভাবে একের পর এক প্রশ্ন করা আলেম সমাজকে অবজ্ঞা করার শামিল এবং আলেমদের কে মনে রাখতে হবে আপনি যখন যে অনুষ্ঠানে যাবেন আপনার সাথে কজন যাচ্ছে এবং তাদের সাথে কজন থাকছে এ বিষয়টি মাথায় রেখেই টিভি চ্যানেলগুলোতে বা টকশোতে যাবেন আপনার পক্ষে যদি একজন থাকে তাদের পক্ষে যদি চার জন থাকে তাহলে ওখানে যাওয়া আপনার উচিত হবে বলে আমি মনে করি না তারা চারজন থাকলে আলেমরাও চারজন থাকতে হবে তাহলেই সঠিকভাবে কথাগুলো তুলে ধরা যাবে।,0,religion
আহারে! এ যদি করা যাইতো🙂 তাইলে কত মুরিদরে করতাম😓 আর তাহসিন ভাইয়ের ফ্যানরা ধইরা ধইরা বাশ দিতো 😌,0,religion
এই ছেলে তো আদব কায়দা ভাল করে জানেনা সেই লোক কি করে ভক্ত দিচ্ছে। আবার বলছে কাউকে আপমান ও হেও করা এই ছেলের উদ্দেশ্য না কিন্তু তো এই গুলো করছে।এই ছেলে তো একবার একটা টিভি রিপোর্টআরের সাথে ভয়ে কথা বলতেও সামনে আসে নাই।,0,religion
এমন আরও অনেক ভন্ড পীর আছে যা ইচ্ছা করলে সরকার এগুলোর ভন্ডামী শেষ করতে পারেন।,0,religion
কোথায় বঙ্গবন্ধু আর কোথায় খলিফা,0,religion
আজকে কমেন্টস না করলে পারলাম না ভাই আপনার চ্যানেলটা করছি অনেক আগে বেশ ভিডিও দেখছি তার ভিতরে এটা সেরা ছিলো। ও এত্তবড় শয়তান বলার অপেক্ষা রাখে না ওর একটা বড় আস্তানা আছে সোঁনারগাওয়ে ওটা এখন অনেক বড় হচ্ছে।,0,religion
কেমন যেন কষ্ট হয় ??? যে মানুষ গুলি শাইখ মামুনুল হকের সাথে কথা বলছে আর ইসলাম সম্পর্কে বিভিন্ন কথা বলছে তাদের তা যোগ্যতা নেই । এইখানে যারা আছেন মামুনুল হক সাহেব ছাড়া তারা তো অসম্প্রদায়িক মানুষ কিন্তু তাদের মনে রাখা উচিৎ জান্নাত একটি সাম্প্রদায়িক জায়গা এইখানে শুধু খাটি মুমিনদের স্থান হবে ওদের মতো ধর্ম দ্রোহিতা সেকুলারদের জায়গা হবে না খারাপ লাগে এই উপস্থাপিকা যেন একজন জজ হিসেবে বিচার করছেন। যত সব নিষিদ্ধ পল্লির বেলুন ফাটা মেয়ে ।,0,religion
শাহরিয়া নাস্তিক,0,religion
দেওয়ানবাগি পাঠারে রোস্ট বানাও বালাকইরা।,0,religion
আল্লাহ তাদেরকে জান্নাতে দিবে আমাদেরকে জাহান্নামের দিবে তোদের কীর্তিকলাপ দেখে মনে হচ্ছে,0,religion
সালার জিনিস কেটে ফেলব,0,religion
কিছু ভন্ড আছে আর তুই বড় ভন্ড পাগলা আহামদ শফী হুজুরের নোখের জগুতা তুর আছে,0,religion
নাস্তিক রা যে এই দেশে কতটা সক্রিয় তা এই ভিডিও দেখলে বুঝা যায়।লজ্জা লাগে আমি এক মুসলিম দেশে বসবাস করি যেই খানে নাস্তিক দের কতটা দাপট।,0,religion
সহবাস স্ত্রী মিলন সম্পর্কে এমন কি আছে এই পোস্টে ? যা অধিকাংশ মানুষ জানে না! যা না জানার কারনে সহবাসের আসল আনন্দ পাই না! বিস্তারিত সম্পূর্ণ কুরআন ও সাহিহ হাদিসের আলোকে ।,0,religion
ঘোড়ার ডিমের জবাব দিসে। এই মামুনুল হকেরা হচ্ছে চোখে একরকম ফিল্টার পরিহিত লোক।,0,religion
আহা এটা কি চায়না ভাষা জিজ্ঞেস করে টিং টং টং বং হং,0,religion
আব্বাছি কে মিজানুর রহমান আযহারির ভুল দরে আব্বাছি মুরক,0,religion
পিচ্চিটারে পিটার দাও আবালের দল তোরা সবাই,0,religion
আল্লাহ সময় মত তাদের কাজের ফল দিবে। আর তা হল জাহান্নাম,0,religion
বলদ টাকে লাত্তি মাইরা ডাসবিনে ফেলেদেন,0,religion
হুজুর আপনি সম্মানিত লোক ।এক বন্ড তাহেরি কথা বলে আপনার মূল্যবান সময় নষ্ট করবেন না ।,0,religion
ওরে জুতার বাড়ী দেওয়া উচিত,0,religion
এটা তার প্রাপ্য,0,religion
ভাই তুমি এগিয়ে চলো আমরা সাথে আছি 🎙️ ইনশাআল্লাহ। জীবন দেওয়ার জন্য প্রস্তুত আছি ইনশাআল্লাহ,0,religion
তাদের জন্য রয়েছে জাহান্নাম।,0,religion
হাইরে নাস্তিক,0,religion
ভাই চালাইয়া জান আমরা আছি আপনার সাথে। 😍😍😍,0,religion
তোমাদের একটা অনুরোধ করি তোমরা আয়াতের অনুবাদ টা যদি পড়ে শোনাতে তাহলে মূরখো লোকদের বুঝতে সহজ হতো ধন্যবাদ।,0,religion
আমি খুব খুশি হয়েছি কারন আপনি আমার অনুরোধ রেখেছেন।,0,religion
তুই বড়ো ভণ্ড,0,religion
মাশআল্লা আল্লাহ তোমাদের কে হায়াত দেক বেশি,0,religion
কবরে গিয়ে বুঝবা সুলতানা কামাল,0,religion
যে এই ভিডিওটা বানীয়েছে সে নিজেকে খুব চালাক ও স্মার্ট মনে করতেছে আসলেই সে বোকা তার জানার বিতরে অনেক ভুল আছে।,0,religion
কাফের এজিদের দালাল মিযান আযারি,0,religion
শয়তান তেৱা ধঁ্শো হয় আমিন,0,religion
তাহেরি নিজেকে সংসোদন করো,0,religion
এসব বন্ডদের অাইনি ব্যবস্তা নেয়া হুক,0,religion
পৃথিবীর মানুষগুলো যদি হুমায়ন স্যারের মত হত তাহলে আজ মানব সভ্যতার এই মানুষগুলো চাপাতির কোপ থেকে অন্তত রক্ষা পেত আজ তা উল্টে পথে হাটে মানবতাবাদ 😒😒,0,religion
জুতা মার,0,religion
তাহেরি তুমার এই জিকির নয় এটা লুচছামি তুমি কতমেয়ের জিবন নযট করেছ আললা ভাল জনেন? তুমি আমার গাধার মত এই কথাটা হাদিসের একটা অংস!,0,religion
অপপ্রচার?সত্য বললেই অপপ্রচার হয়ে যায়!!,0,religion
মক্কা মদিনা আমদের আদর্শ হবে কেন? মুসলমান দের আদর্শ হল কুরআন সুন্নাহ নবি মুহাম্মাদ সল্লাল্লাহু আলাইহি ওয়া সাল্লাম। কোন দেশ কি করে দেখে লাভ আছে? মুসলিম দের লক্ষ্য জান্নাতে যাওয়া আল্লাহ সকল হুকুম আহকাম মেনে। এটা ত এক্ টা ছোট বাচ্চা ও জানে। শুধু চা তে গোফ ভিজিয়ে ভিজিয়ে খেলে হবে না তো,0,religion
এসব ভন্ড দের আল্লাহর গজব দিক,0,religion
উপসথাপিকা ঔ বদমাইশটাকে দূইটা লাথি মেরে মাথায় পরদা করতে বলুন,0,religion
ভন্ডামিকে প্রশ্রয়দাতা সংশয় অামাদের সরকার,0,religion
এডমিন একজন নাস্তিক সবাই তার জন্য দোয়া করেন আল্লাহ যেন তাকে হেদায়েত দান করেন আমিন,0,religion
আল্লাহ দোহাই তোমার এই নাস্তিক লোপা কে তুমি ধ্বংস করে দাও আর সহ্য করতে পারিনা আল্লাহ।,0,religion
আসলেই তোরা নাস্তিক। মাওলানা মামুনুল হক সাহেব এগিয়ে যান আমাদের দোয়া এবং আল্লার রহমত আছে থাকবে।,0,religion
ভাই ভাই এমন একটা ভিডিও বানানোর জন্য আপনাকে ধন্যবাদ অনেক অনেক ধন্যবাদ,0,religion
আগের মতো কোরআনের আলোচনা হয়না বলে এতো মাহাফিলে ভনডোদের দেখা যাচ্ছে,0,religion
মুফতি আমির হামজা কে দরকার ছিল,0,religion
দেওয়ানবাগী যেমন ভন্ড প্রতারক জাহান্নামে ঠিক তুমিও ভন্ড জাহান্নামী তার কারণ তুমি মানুষের মান সম্মান নিয়ে টানাটানি করো এই অধিকার আল্লাহ কাউকে দেয়নি আমিও দেওয়ানবাগীর ঘোরবিরোধী মোনাফেক,0,religion
এই ধরনের ভনড পীরদের জন্য অনেক মুসলিমের ইমান নষ্ট হয়,0,religion
ভাইয়া এমন অনেক ভন্ড আছে দেশে সেগুলাকেও রোস্ট করেন।,0,religion
আপনার বিরদ্দে ব্যাস্তা নেওয়া হবে।না জেনে ত্যাত দেওয়ার জন্য।,0,religion
বাংলাদেশে মনে হয় কোনো মুসলমান নাই কারণ একেক সময় একেক ভন্ড পীর আবিষ্কার হয় আর তাদের অনুসারী যোগাড় হয়ে যায় কিন্তু প্রতিবাদ করার মতো কেউ নাই।,0,religion
ইসলামকে ধ্বংস করার জন্য এক হাজার নাস্তিকের চেয়ে এক জন আহলে খবিস লা মাজহাবি যথেষ্ট ।।।,0,religion
আল্লাহ হুযুরকে নেক হায়াত দান করুক 👉👉আমিন,0,religion
গজব,0,religion
তোরে যদি একবার পাইতাম তাহলে থাপরাইয়া দাঁত হালাইয়া দিতাম,0,religion
তাহসিন ভাইয়ের ভিডিও মানেই জোস !❤️ আগুন টা ঠিক জায়গায় ই লাগছে ! ভালবাসা অবিরাম ভাই ♥️♥️,0,religion
শাহারিয়ার কবির তুই তোর বাপেরে মডেল মনে না করে চাচারে মনে করিছ।কারণ হেইডা ও তো তোর দাদার পোলা।কোন ধর্ম সম্পর্কে জানতে।তার অনুসারীকে নয়???ধর্মগ্রন্থকে দেখতে হবে।আমি কোন দিন কোনো ফতোয়া দেয়নি।আজকে বলতে ইচ্ছা করছে তুইএকটা না তোরা চার টা নাস্তিক নাস্তিক।।।,0,religion
এই সব নাস্তিকদের সাতে কতা বলতে গেছেন কেন,0,religion
আমি মনে করি এই নাস্তিক লোপার যদি প্রকাশ্যে ওর শরীরে আগুন ধরানো হয় তাহলে অন্য নাস্তিকরা ও ভয়ে আর এধরনের কথা বলার সাহস পাবে না,0,religion
আপনার ভিডিও টি হাজার হাজার দেওয়ানবাগীর উত্তরসূরি দেখে আনলাইক দিয়ে পালাইছে 😎,0,religion
আসসালামু আলাইকুম ভাই বিষয়টা হলো যে আপনার দেওয়ানবাগী হুজুর নিয়ে যে ভিডিওটা পাঠিয়েছেন আপনি কি ওনার সম্পর্কে আসলে সত্যি ধারণা আছে আপনার সম্পর্কে কোন ধারণা নাই শুধু শুধু কেন একটা মানুষের নামে মিথ্যা অপবাদ করে আপনাদের কি লাভ শুধু বিয়ে পাওয়ার জন্য ইউটিউব এ কিছু টাকা পাওয়ার জন্য একটা মানুষ সম্পর্কে জানবেন তারপর বলবেন যদি একটা মানুষ সম্পর্কে উল্টাপাল্টা কিছু কোন মন্তব্য করেন আপনি জানেন এটা কি বোর্ড করা হয় বলা হয়েছে কি না কি বললে না জেনে শুনে সে নাকি তার মায়ের সাথে যিনা করা হয় আপনি আমার কথাটা যদি না হয় আপনার জন ব্যক্তির সাথে কথা হুজুর গন করে দেখে আমি চাইনা আপনার মায়ের সাথে যিনা করেন,0,religion
খুব ভালো লাগলো ভাই,0,religion
প্রিয় দ্বীনি ভাই!আমার চ্যানেলটি সাবস্ক্রাইব করুন প্লিজ৷,0,religion
নবীর ইস্তিরি খাদিজা নাকি ইন্টেক ছিলেন না। সেই কথা ও মিজানুর রহমান আজহারি বলেছেন। নবী দুষমনি জে করবে। তাকে ভাল হক্কানি আলেম হলেও তার কল্লা দিতে হবে।,0,religion
এই কুওারা মোকা মদিনার কথা বলছেন মোকা মদিনার আইন হলে এই কুওাদের আগেই কদল করা হত,0,religion
ওয়াজে সালায় গান গাইতে শুরু করেছে ছিঃ ছিঃ ছিঃ জগুন্য,0,religion
আমার মন থেকে তোকে ঘৃনা করি। আল্লাহ্ তুমি এর পায়সালা করো,0,religion
এই বনড আমি সব কয়টা কমেন্ট দেখলাম সবাই সিদ্দিক হুজুরের পক্খে কথা বলে,0,religion
জন নাস্তিক কে একসাথে ধোলাই দিলেন আল্লামা মামুনুল হক,0,religion
যে গুলা এই ভিডিওতে ডিস লাইক দিছে ঐ গুলা দেওয়ান বাগির পুতাইত,0,religion
চোখে জল আসল! আল্লাহ তুমি হক পন্থি আলেমদের হেফাজত কর ৷ আমিন ৷,0,religion
শিশু বক্তার বয়স কত আরেক জনের গিবদকরে অর গেনের অভাব,0,religion
এই সমস্ত ভন্ডদের আমাদের মতো কিছু মুসলমান আছে যারা এদেরকে ছাপর্ট এবং সহযোগিতা করে!! আমরা যদি একটু সচেতন হই তাহলে এই দুই পা ওয়ালা জানোয়ার গুলা আার সহস পাবে না!!,0,religion
সবচেয়ে বেস্ট ডক্টর জাকির নায়েক সে আমাদের মুসলিমদের জন্য সঠিক অনুসরণকারী হাজার বছর বেঁচে থাকুক ডক্টর জাকির নায়েক আমিন,0,religion
ভনডো তাহেরি তুই ভালো হইয়াজা নয়েতো তোরে জুতা পিটা করমু ইহুদির দালাল,0,religion
সময় উপযোগী দারুন ধোলাই ভিডিও,0,religion
দুনিয়ার কোনো মানুষ আমার নবী স এর শিক্ষক নয় মহান আল্লাহ স্বয়ং তিনার শিক্ষক যখন জিবরাইল আ রাসুল স কে বললেন ইকরা অর্থাৎ পড়ুন তখন কিন্তু তিনি চুপ ছিলেন তারপর যখন আল্লাহ তাকে পড়ার শক্তি দিলেন তখন তিনার ওপর নাযিল হলো সূরা আলাকের প্রথম আয়াত,0,religion
হুজুর ঠিক বলেচেন,0,religion
বদমাইশের ঘর বদমাইশ মাজার পুজারি।,0,religion
ফাশি দেয়া হোউক,0,religion
ভাই অামি অাপনার একজন হিন্দু ভক্ত ৷ কিন্তু অাপনার ভিডিও অাসলেই অনেক জোস ৷ সব ধর্মেই ভন্ড অাছে ৷ অাশা করি সমাজ থেকে এসব ভন্ড একদিন চিরতরে নির্মূল হবে ৷,0,religion
আরে ভাই তার বিয়ে করা বৌ কে বলছে সে ত বলে এক মত হয়ে তার মায়ের সাথে সেক্স করতে তার মানে এই তার সেক্স সঙ্গী যে কারো সাথে সেক্স করবে তার কোন বাধা নেই,0,religion
চার নাস্তিক রে জুতা দি মার,0,religion
এই সব মাজার ভক্তদের শিরচ্ছেদ করা উচিত,0,religion
তুমি তো এখনও লেদা ছেলে। ওলামায়ে কেরাম সম্পর্কে কি বুঝ তুমি? বাচ্চা মানুষ! হা হা হা,0,religion
আমার মনে হয় আপনারা এক দরনের কলংক,0,religion
নাওজবিলা।।😖😟,0,religion
আল্লামা তাহেরী হুজুরে বিরুদ্ধে কথা বলবার সাহস দিলকে ভন্ডর বাচ্ছা,0,religion
হা ভাই ভালো লাগছে বিডিওটা,0,religion
আমির হামযা ঠিক বলছে,0,religion
ভাই তুমি সেরা দিছেন ভইড়া 😂😂😂,0,religion
আমারও থাপ্পড়াইতে ইচ্ছা করে দেওয়ানবাগী সহ তার মুরিদ সহ,0,religion
ভাতিজার পোত মাথা কামানো কি নবীর সুন্নত না রে,0,religion
আমি বুঝেগেছি আপনি এখনো দুধের বাচ্চা আপনার ওয়াজ করার বয়স হয়নাই ? যদি‌ বয়স হয় তাহলে আজহারীর কাছে গিয়ে শিক্ষেন ? বড় একজন বক্তা হতে পারবেন ? আপনার এতো অহংকার কিসের ? হ্যাঁ এটাই সত্যি ?,0,religion
কথা একদম ঠিক বলছে,0,religion
ভাই আর বইলেন না আমার এক রিলেটিভ আছে একদিন জাস্ট বলছিলাম যে পীর দের সিজদা দেওয়া উচিত না একমাত্র আল্লাহ ছাড়া। বলা মাত্রই আমার উপর কথার বৃষ্টি 😂 উনাকে কিছুতেই বুঝাইতে পারলাম না।কারন উনি এই পীরের ভক্ত 😁😁😁 আর এই পীর নাকি সাথে করে জান্নাতে ও নিয়ে যাইতে পারে।😁 নিজে ভালো না হইলে কারো ও ক্ষমতা নাই এক আল্লাহ পাক ছাড়া জান্নাতে প্রবেশ করায়।,0,religion
মুখ। মানুষ তাই এ অবসতা,0,religion
জার যেটা বুঝ দারি পালিয়ে রাখে মুজ তাতে তদের কি নিজের চিন্তা কর,0,religion
আমার মনে হয় তাহেরীর পাশে যাদের কে দেখা যায় তাদের কে ও টাকা দিয়ে ভাড়া করে আনে যাতে লোকজন বুঝতে না পারে যে তাহেরীর মাহফিল কেউ শুনতে আসেনা।,0,religion
? এই চিহ্নটা ব্যবহার করতে হলে বাক্যটি তে অবশ্যই কি কী বা কোথায় ইত্যাদি দিয়ে প্রশ্ন করতে হবে। আশা করি বুজতে পারবেন!!,0,religion
বড় বন্ডের রোস্টেড করেছে ছোট বন্ড।,0,religion
হালায় দূর্বল হাদীস কইছে।,0,religion
চোর দেয়ান বাগি,0,religion
এই মহিলা কাফের শয়তান। ওলিপুরির নাজায়েজ গার্লফ্রেন্ড,0,religion
অত্যান্ত ভালো লাগলো,0,religion
আহলে হাদিসরা কিছু মানতে গিয়ে শিরিক বা কুফুরি করলেও দোষ নেই মাযহাবীরা কিছু করলেই দোষ হা হা হাশি পায় এরাই হলো মুলতো মন পুজারি কিসের এরা হাদিস মানে সব ফালতু ৷,0,religion
তোর চুল বড় কেনো বুঝলাম। কিন্তু তোর দাঁড়ী তো একমুষ্ঠী নাই। তুই ভন্ড ভন্ড ভন্ড।,0,religion
এগুলারে অাল্লাহ সব চেয়ে বড় শাস্তি দেক,0,religion
আমার মরার আগে আমি দেওয়ানবাগির মরার দিনটি দেখতে চাই!তার মরা টা কেমন হয় আমি এটুক দেখতে চাই😑,0,religion
ভাই তাহেরি কই,0,religion
কথা বললেই কি হবে এইটা কে মারণা কেন,0,religion
এরা ইসলামের চির শএু,0,religion
মিজানুর আজহারি কে বড় করতে গিয়ে কিছু হককানি আলেম দের দুশর করলি কেনো জেমন ইলিয়াচুর রহমান জিহাদি নুরুজজামান নোমানি এরা হককানি আলেম,0,religion
শয়তান থেকে বড় শয়তান,0,religion
গিদর পাল নিয়েই আসে উপস্থাপিকা কি নিরপেক্ষ ছিলো ? তারা ইসলাম বিরোধী কথা বলবে কিন্তু বলা যাবে না ! এরা শুধু ইসলাম নয় দেশটাকেও ধ্বংস করছে।,0,religion
তবে ভারতে কেউ কে কাপের বলেন নাই অাল্লাহু তাদের কে অাব্বাসির ফতুয়া থেকে বাঁচাইছে।,0,religion
খুব সুন্দর উত্তর,0,religion
আমি দেখছি অনেক লোক পির কে সালাম করে আর টাকা দেশ। যে বেশী টাকা দেয় তাঁর সাথে ভাল ব্যবহার করে আর যে টাকা কম টাকা তার সাথে ভাল ব্যবহার করে না,0,religion
মারহাবা হুজুর সুন্দর উওর দিলেন,0,religion
কিছু বক্তা অাছে টেজে ওটার পর মন্দ ছাড়া আর কিছু খোজে পায় না।,0,religion
দেওয়ানবাগ কে জুতা পেটা কোরতে চান কে কে এক টা লাইক দিয়ে জানিয়ে দিন,0,religion
যতো ভন্ড সব বি বারিয়া 😂😂,0,religion
দারুন সত্য কথা,0,religion
ও রে ভালো লাগে কারন সে একটা কৌতুক,0,religion
মোহম্মদ হঃ সঃ একজন মহান মানুষ ছিলেন কি? পুত্রবধু জয়নবকে বিয়ে করা হালাল করতে আয়াত নাযিলঃ জয়নব ছিল মুহাম্মদের ফুফাতো বোন। মুহাম্মদ তার ফুফাতো বোনকে নিজ পালক পুত্রের সাথে বিয়ে দেন জোরপূর্বক। জয়নব ও তার ভাই এই বিয়েতে রাজি ছিলো না। কিন্তু মুহাম্মদ কোরানে নিম্নোক্ত আয়াত ডাউনলোড করে ভয় দেখিয়ে জয়নব ও তার ভাইকে রাজি করায় বিয়েতে। আপনারা বিস্তারিত জানতে আয়াতটির তাফসীর ঘেটে দেখে নিতে পারেন। ? আল্লাহ ও তাঁর রসূল কোন কাজের আদেশ করলে কোন ঈমানদার পুরুষ ও ঈমানদার নারীর সে বিষয়ে ভিন্ন ক্ষমতা নেই যে আল্লাহ ও তাঁর রসূলের আদেশ অমান্য করে সে প্রকাশ্য পথভ্রষ্ট তায় পতিত হয়। এভাবেই ফুফাতো বোন হয়ে গেলো তার পুত্রবধু! এর অনেক দিন পর একসময় মুহাম্মদের নজর পড়ে জয়নবের উপর। জয়নব ব্যাপারটা বুঝতে পেরে তার স্বামী জায়েদকে জানায়। জায়েদ ভালো করেই জানতো যে মুহাম্মদ যা চায় তা আদায় করেই ছাড়ে। জায়েদ ভয় পেয়ে যায়। সে খোলাখুলি পালক–পিতাকে বললো “আপনি হয়ত জয়নবকে পছন্দ করেছেন। সে ক্ষেত্রে আপনার জন্য আমি তাকে ত্যাগ করছি।”এ কথা শুনে মুহাম্মদ উত্তর দিলেন “তুমি তোমার স্ত্রীকে রাখতে পারো।” অবশ্য জোড়াজুরি করলে আমি নেবো কিন্তু জায়েদ জানতো যে নবী তার বাসনা চরিতার্থ করবেই। তাই সে শেষ পর্যন্ত জয়নবকে তালাক দেয়। কিন্তু জায়েদ তালাক দিলে কি হবে বাধা তো আরেক জায়গায়। জায়েদ যে মুহাম্মদের পালিত পুত্র আর মুহাম্মদ কি করে পালিত পুত্রের স্ত্রীকে বিয়ে করবে? তখন আরবে পালিত পুত্রদের নিজ পুত্রের মতই দেখা হতো। সুতরাং মুহাম্মদ বুদ্ধি করে একটা আয়াত পয়দা করে দিলেন কুরানে এই বলে যে পালিত পুত্র কোন পুত্রই নয়। তোমাদের পোষ্যপুত্রদেরকে তোমাদের পুত্র করেননি। এগুলো তোমাদের মুখের কথা মাত্র। ব্যাপারটা একবার ভা,0,religion
আসসালামু আলাইকুম শান্তনু ভাই যাজাকাল্লাহ খাইরান ভাই ভন্ড মুশরিক পিরদের মুখোশ উন্মোচন করেছেন ভালো কিন্তু আপনার তালিকা থেকে বরিশালের পির বাদ দিলেন কেনো যেই পিরের বইতে লিখা থাকে আল্লাহ্‌ র আন্দাজ নাই যেই পিরের আকিদা যিকির করিতে করিতে বান্দা আল্লাহর সাথে মিশে একাকার হয়ে যায় মুরিদ দেরকে জাহাজে করে জান্নাতে নিয়ে যাবার গ্যারান্টি দেয় তাকে নিয়াও কিছু বলিয়েন,0,religion
বাংলাদেশের ভন্ড আলেম,0,religion
নাউজুবিল্লাহ!!!!! এরা মুসলিম না মুসলিম নামের কলক্ক ইবলিসের দল,0,religion
উপস্থাপক কে জুতা মারা দরকার সে পক্ষ থেকে ফাজিল,0,religion
বক্তা মিথ্যাবাদী ওনাকে গণধোলাই দেওয়া উচিত কুরআনের মাহফিলে বাজে মন্তব্য করে কেন?,0,religion
নাস্তিকদের মেরে ফেলা হোক,0,religion
দেওয়ানবাগি কে ফাসি দেওয়া হক,0,religion
এই নাস্তিক কে দুই পাঁ ধরে এক টানে মুরগি ফারার মত রাং ফারা করতে হবে।,0,religion
দেওয়ানবাগীর মুরিদদের কথা শুনে আমার শরীরের রক্ত খালি টকবক করছে মনে হচ্ছে যদি ক্ষমতা বা এমন কোনো পাউয়ার আমার থাকত তাহলে দেওয়ানবাগী আর তার মুরিদদের গুলি করে মারতাম ?,0,religion
উপযুক্ত বিচার করা হোক,0,religion
হে শয়তান,0,religion
কেন এসব ভিডিও বানিয়ে গালি সুনেন।,0,religion
কিয়ামতের আলামত দাজ্জাল😡,0,religion
ঠিকআছে! কিন্তু বোরহান ভাই মাঝে মাঝে সিনেমার অংশ না দেখানোই ভালো। ওগুলো আসলে আপনার সাথে যায় না।,0,religion
হালকা পাতলা ভন্ডামি,0,religion
শয়তানের দৃশ্যমান রুপ গাব গাছি।,0,religion
আল্লাহ এই রকম নাস্তিক ছেলে মেয়েকে অবশ্যই কঠিন শাস্তি দিবে ইনশাল্লাহ!🇧🇩,0,religion
সবাই বাচ্চাদের ওয়াজ শোনা থেকে বিরত থাকি,0,religion
ভাই অনেক দিন ধরে বলতেছিলাম দেওয়ানবাগী কে রোস্ট করেন ধন্যবাদ রোস্ট করার জন্যে,0,religion
মিজানুর রহমান আজহারী আমি আপনাকে খুব ভাল বাশি আল্লাহ্‌ যেন আপনাকে সবসময় ভাল রাখুক,0,religion
বিবাড়ীয়া সিলেট বিভাগে নয় ভাই। চট্রগ্রাম বিভাগে পড়েছে। জেনে কথা বলবেন বা ভিডিও বানাবেন।।,0,religion
এই পিচ্চির বয়স কত? 😡,0,religion
তিনি যে ভন্ড তার গালিতেই বুঝা যায়।,0,religion
জুতা মারি তোর গালে তাহেরী,0,religion
তাহেরীর কথা সত্য আর আজহারীর কথা মিথ্যা,0,religion
মাওলানা সাহেব ওয়াজ করার আাগে জানুন। আপনি একজন পাপী। পীর সাহেব হওয়া এত সহজ কাজ নয়।,0,religion
আল্লাহ পাকের জিকির নিয়ে সবচেয়ে বেশি ভন্ডামী করে তেহেরী তারে পুরান জুতা দিয়ে পিটানো দরকার,0,religion
যাহারা ডিসলাইক দিয়েছে তাহারা দেওয়নবাগীর মুরিদ আবাল! তাই লাইক হবে।,0,religion
নাস্তিকের সাথে কোন কথা নয় তাদেরকে উচিৎ শিক্ষা দিতে হবে গজারী পেটা। এরা ইসলাম বিরোধী শয়তানের দোসর জাতির চিহ্নিত শত্রু এরা বিশ্বব্যাপী ট্রাম্প আর বুশ আর পৌত্তলিকদের অনুসারী। তাদের সাথে তর্ক বা বসা চলে না। জাহান্নামের লাড়কি এরা। অসভ্য নিকৃষ্ট জানোয়ার এইসব মোচওয়ালা চুলওয়ালী নাস্তিক কুকুর। তাদের উপর আল্লাহর লানত যারা ইসলাম রাসুল সাঃ ও আলেমদের উপর বিষোদগার করে। দুনিয়াতে মৃত্যুর সময় এবং মৃত্যুর পর পরই ওদের আল্লাহ তাআলার কঠিন শাস্তি আরোপিত হবে।,0,religion
মিজানুর রহমান আজহারীকে ভন্ড যে বলবে সে হচ্ছে একটা কাফীর,0,religion
এসব জিকির না করাটা বালো,0,religion
আমি হলে সব কয়টাকে মারতে শুরু করতাম মামুনুল হক সাহেবের মাথা খুব ঠান্ডা ছিলো,0,religion
সেই মুনাফেক যে অশ্লীলভাবে গালাগালি দেয়। সহিহ বুখারী হাদিস নং আল্লাহ তা‘আলা অশ্লীল এবং কটুভাষীকে অবশ্যই ঘৃণা করেন। সুনান তিরমিজী হাঃ নং ইসলামে গালিগালাজ সম্পূর্ণ নিষিদ্ধ। আর অশ্লীল গালিগালাজ মুনাফিকির একটি বৈশিষ্ট্য।,0,religion
জোকারের বাচ্চা জোকার,0,religion
কুসচক্তে কই কি সালা দেওয়ান বাগি,0,religion
এই কুকুরদের কে জুতা পিটা করে দেশ থেকে বিতারিত করা দরকার।,0,religion
কুত্তা একটা মানুষের লগে লাগছে,0,religion
মিজানুর রহমান অসাধারণ বক্তা,0,religion
এই আইডির ওয়াবিদের জুতা দিয়া পেটানো উচিত,0,religion
মাজার পূজারি ভন্ড লোকটাকে একটা জুতার বাড়ি দেয়া দরকার,0,religion
দেওয়ান বাগী কে জুতাপিটা করা হক,0,religion
উনি সয়তানের বাচ্চা আর উনাদের খোদা শয়তান,0,religion
হুজুরসতিবলেছে,0,religion
এখানে অপমানের কিছুই দেখা যাচ্ছে না।,0,religion
ঐ সয়তান তোকে ইসলাম ধর্ম ভালো লাগে না তুই অন্য ধর্মে চলে যা তাতে আমাদের কোন জায় আসেনা কিন্তু বারা বারি করা বন্ধ কর টাকার লোভে পরে নাস্তিক হয়েছিশ তো তোর পরিনতি হবে ফিরআউনের মত অপেক্ষায় থাক শুনেরাখ ইসলাম হচ্ছে খাটি সোনা তুই জতই ভেজাল ঢুকার চেষ্টা কর লাভ হবেনা কারণ জারা সোনা চেনে তারা ঠিক সোনা কিনবে তারা খকনো তোর বিকৃ হবেনা তুই তো সালা সেয়াল গর্তের ভিতরে ঢুকে ভুক ভুক কর্তেছিস ঐ সয়তান পয়সার উপর জদি তোর এতোই লোভ তাহলে সেয়ালের মত গর্তের ভিতরে না থেকে আরব বিশ্বে চলেজা সেখানে রমজান মাসে ফকির দের কে কোটি কোটি টাকা দান করে সালা নাস্তিকের বাচ্চা কুত্তাও মালিক চেনে এরা কুত্তার চেয়েও জঘন্য,0,religion
ভন্ড মাজার পূজারীর হাজার মুরিদ ডিজলাইক দিয়ে নিজেদের অবস্থান জানান দিসে 🙈,0,religion
ভাই কাওকে পাচ্ছিনা কথাটা বলার জন্য আপনাকেই বলি ভাই বাংলাদেশে নাকি সেক্স ইস্কুল হয়েছে সে খানে নাকি ছেলে মেয়েদের সেক্স বিষয়ে শিখানো হয় প্লিজ ভাই এই বিষয়ে কিছু বলোন একটা ভিডিও বানান এমনিতেয় ভাই বাংলার মেয়েরা যে সাব শুরু করছে যেমন তাতেই তে আসতে মন চাইনা পরে দেশে যেতে মন চাইবেনা প্লিজ ভাই একটা কিছু করেন,0,religion
কিছু দেওয়ান বাগীর অনুসারী দেখতে চান ডিসলাইক চেক করুন ভালো একটা বড় গান দেখতেও বোরিং লাগে কিন্তু বস তোমার ঘন্টার ভিডিও হলেও শুধু দেখতেই মন চায় ভালবাসবো অবিরাম😍😍😍,0,religion
ধন্যবাদ ভাই আপনাকে,0,religion
এইসব ভন্ডদের জন্য দেশটাই ধংস হচ্ছে,0,religion
সালা তুই কিসের হুজুর তুইত একটা ছোট বাচ্চা তুইযে আরেক হুজুরের গিবত করসিস। তুর কতটুকুন এলেম আছে। মানুষ দেখানো ওয়াজ না আওয়াজ বন্দ কর।আরেক জনের গিপত করার আগে ভালো করে কোরআন হদিসের এলেম শিখে নিস।,0,religion
এখানে আব্বাসীর কি অপমান হলো গাধা এডমিন কি দেখচে দুর।,0,religion
এই চার নাস্তিকদের কে জুতা পিটা করার দরকার,0,religion
ধম ধম ধম এ সব বলে সাধারন মানুষের মাথাটা নষট করাটাই তদের কাজ। এতে নিজে নিজের মাঝে নষট হয়ে যাবে একদিন।,0,religion
আপনার গিবাত করার জন্য ধন্যবাদ আপনাকে বলি গিবাত করা আর নিজের মায়ের সাথে যেনি করা সমান জানেন না,0,religion
জন দেওয়ানবাগীর মুরিদ৷ 😭😭 আল্লাহ এদের বুঝার তৌফিক দান করো 😭,0,religion
মাজার পুজা কি ভাবে করে আমি জানি না বাট এইটা বলতে পারি শাহজালাল রাঃ এই দেশে ইসলাম প্রচার করেন এখন আমরা মানুষ যদি এর অপব্যবহার করি তার আশে পাশে মধ গাজা খাই এইটা কি আমাদের দুষ নাকি অলিদের দুষ? তবে আমরা মাজার পুজা করি না আমারা তাদের মাজারের পাশে গিয়ে দারিয়ে অনুতপ্তহই মনে একটা শান্তি পাওয়া যায় নিজেকে খুব ছোট মনে হয় তবে আমরা উনাদের উসিলায় আল্লার কাছে প্রার্থনা করি মনে একটা শান্তি ই পাওয়া যায় কে কি করল এইটা আমার দেখার বিষয় না আমি যদি দেখার উদেশ্য যাই তবে দুষ চোখে পড়বে যদি মন থেকে অনুতপ্ত হয়ে যাই তবেই শান্তি মিলে আল্লাহুয়াকবার,0,religion
কুকুরের মত ওয়াজ,0,religion
শাহরিয়ার মুরগি চোরের কথা শুনলেই মেজাজ খারাপ হয়,0,religion
ফাসি চায়,0,religion
আপনি কি তাহেরি ব‌উ তার সম্পর্কে সব জানেন যা বলছেন সব সঠিক,0,religion
ওয়াজ শুনতে ভালো লাগে কিন্তু বেশির ভাগ ওয়াজ গুলোতে সৃষ্টি কর্তার আলোচনার থেকে হুজুর দের সমালোচনা টা বেশি শুনতে পাই আমার মনে হয় সমালোচনা না করে আত্ম সমালোচনা করার মাধ্যমে সেই পরম প্রেমময়ের গুন কীর্তন করলে আত্ম শুদ্ধির পথ প্রশস্ত হবে ভুল হলে মার্জনা করবেন,0,religion
তুমি ছাত্র মানুষ তোমার বাবার বড় ওস্তাদের সমতূল্য আলেমদের নিয়ে তুমি কথা বলছো তোমার মুরুব্বিরা তো তাদের বহাস থেকে বহু বার পরাজিত হয়েছে যার প্রমান বহু দেখছো তোমার মত বেয়াদপ ছেলে কম ই দেখছি বাপের আগে বাল পালাও আগে শিখো তার পর ওয়াজ করো।,0,religion
নিজে আগে ঠিক হও।বন্ড জানি কোনান কার।,0,religion
কুত্তা র আওয়াজ,0,religion
তোর সামনে যারা বসে আছে তারা হলো আসল গাধা তারা কিভাবে তোর মত পিচ্ছির ওয়াজ শুনে এবং ওয়াজ করতে দেয় তোকে,0,religion
আল্লাহ এদের হেদায়ত দাও,0,religion
না জেনে কথা বলবেন না,0,religion
নাস্তিক চ্যানেল ও চার নাস্তিক,0,religion
বাই। এই শয়তানের মুখ দেখা হারাম।দোউয়ানভাগি সে একটা দাজ্জাল। ভাই তোমরা এগিয়ে যাউ?,0,religion
নাস্তিক জন জন আলেম,0,religion
দেওযানবাগির তো কপাল খারাপ ওর আসেক জারা তাদের ও,0,religion
হে আল্লাহ তুমি তাকে হেদায়েত করুন।,0,religion
হাফিজুর রহমান সবচেয়ে ভালো বক্তা তিনি কাউকে গালমন্দ করেন না তার ওয়াজ মাহফিল সবচেয়ে ভালো তাকে ভন্ড ভলার অধিকার আপনাকে দিয়েছে কে আপনি না বুঝে কাউকে ভন্ড বানাতে পারেন আপনি তাহলে নাস্তিক হয়ে যাবেন আল্লাহ আপনাকে ক্ষমা করুন,0,religion
এর পরে হিজবুত তাওহিদ নিয়া ভিডিও করেন ভাই,0,religion
নাস্তিকের বাচ্চারা বাংলাদেশ মুসলিমদেশ এটা ভুলে যাস কেন ইসলাম শান্তির ধর্ম ইসলাম অন্য ধর্মের লোকদের অবশ্যই সমান অধিকার দেয়,0,religion
ভন্ডদের গালে জুতা মারা উচিত,0,religion
ওরে যদি মুফতি বলা হয় তাহলে মুফতি দের অপমান করা হবে আপু আপনার কথা গিলো অনেক ভালো লাগে তাহেরিরে দেখলে মনডা চার ওরে জবো করি 😈😈😈,0,religion
এগুলা নিয়া ঝগড়া করা ঠিক না আসলে কিন্তু গাধা কিন্তু খাওয়া সঠিক,0,religion
বাবুরে হেতের কথার কি ডায়লগ,0,religion
দেউয়ান বাগি কে রাস্তায় কুকুরের মত ফেলে মারা দরকার,0,religion
এদের চে ইহুদিরা অনেক ভালো,0,religion
তাহেরি শুধু বন্ড না ইমান হারা শিরককারী কাফের।এ কাফের আরও অনেক মানুষ কে শিরকে লিপ্ত করছে।আল্লাহ এ কাফের থেকে জাতিকে রক্ষা কর।,0,religion
লা মাজহাবী সব গুলো ফেৎনাবাজ।,0,religion
বাংলাদেশই খালি এইধরনের ভন্ডামি চলে।অন্য কোন দেশে এরকম ভন্ডামির জায়গানায়।,0,religion
আল্লাহ তুমি ওদের মুখে গজব ফালাও,0,religion
ভাই জিহাদি হুজুর হক্ব পন্থি হুজুর উনাকে নিয়ে এইটা করা ঠিক হয়নি। আশা করি ঐ ভিডিও টা ডিলিট করে দিবেন। আর ঐ বিষয়ে আর ভিডিও চাচ্ছি না,0,religion
দেওয়ানবাগী ভন্ডর ফাসি চাই,0,religion
সবাইকে ঈদ মোবারক,0,religion
ভন্ডদের কারনে ইসলামের ক্ষতিহচ্ছে।,0,religion
জারক,0,religion
আপনাদের নতুন ভিডিওর জন্য অপেক্ষায় থাকি।,0,religion
নতুন নতুন শালা ওয়াজ না করে।খালি গিবত।,0,religion
নাস্তিক গুলোর সাথে কথা না বলাই ভালো ছিলো আল্লাহ্‌ তুমি এই নাস্তিক গুলোর বিচার কইরো,0,religion
আমি ভারত থেকে বলছি সালা মোনাফেককে জোতা পেটা করুন,0,religion
এই জনের জন্য আল্লমা মামুনুল হক এর দরকার নাই আমি একাই,0,religion
ভণ্ডা বওাঃ,0,religion
হুজুরের সব কথা ঠিক বলছেন,0,religion
তাদের উপর আল্লাহ গজব আসবে,0,religion
আমি বুঝি না হালায় দেওয়ানবাগীর আস্তায় সুন্দরী সুন্দরী মহিলারা যায়া কি করে?,0,religion
তাসিন ভাই হিজবুদ তাওহিদ নামক একটা ভন্ড গ্রুপ আছে। তাদের করুন ভাই। একমত তারা লাইক দেন,0,religion
প্রথমে বলি ওই অসভ্য মহিলা সহ যে কয়জন নাস্তিকের বাচ্চা আছে সবাই কে জুতা দিয়ে পিটিয়ে মারা উচিত বিশেষ করে ওই ডাইনি মহিলার।।,0,religion
আল্লাহ তুমি তাদের শাস্তি দাও।।।না হয় হেদায়াত দান কর,0,religion
ভাই সব হুজুর এক নয় এটা মাথায় রাখতে হবে,0,religion
হায়রে বন্ড হুজুর তুই একটা ভন্ড হুজুর ভন্ড ভন্ড ভন্ড ভন্ড ভন্ড ভন্ড ভন্ড ভন্ড তুই,0,religion
হায় বাংলার মানুষ তোমারা কথাই।।।,0,religion
যারা ইসলাম কায়েমের জন্য জীবন দিতে পারে তারা কোরঅান অাগুন দিবে এটা বিশ্বাস হয়না।এটা অাওয়ামিগীগ দিয়া জামাতের নাম দিয়ে ছে। এটা অাওয়ামিলীগ কাজ। জনগন এখন এত বলদ না।,0,religion
মুরুব্বীর কথা ঠিক। বেক্কেল হল বক্তা।😡😡,0,religion
আল্লাহ তোমার কাসে বিছার দিলান।,0,religion
আমির হামজা কিচু জানেনা,0,religion
এই নাস্তিকের জনসম্মুখে ফাসি চাই।,0,religion
আলেম ওদের অনুস্ঠানে কম যাবেন কারণ ওরা আপনার মযাদা দিতে পারবেনা,0,religion
কি লিখবো ভাই,0,religion
বাই।বাংলাদেশ টেলিবিসন।পাগল,0,religion
এই না জানে কোরান না জানে হাদিস এরে দিয়া করে মাহফিল। এয়া আল্লাহ তুমি রহমত করুণ,0,religion
অগ্রিম ঈদের দাওয়াত রইল সকল মুমিনদের কে ঈদ মোবারক 🌹🌹,0,religion
ভাই ও জুতা খুলে পেটানো শুরু করেন আমরা আছি।,0,religion
আমির হামজা😍😍😍😍,0,religion
মুরগী চোরা বেশি ভাড়াভাড়ী করছ।টা নাছতিক।,0,religion
তোর বাপ কি তোকে জন্ম দেয় নাই? নাকি এমনি এমনিই পয়দা হইছছ। তোর কাছে যদি মনে হয় যে তোর বাবা তোকে জন্ম দিয়েছে তাহলে তোর বাবার নসিব কতইরা খারাপ! তোর বাবাও তোর কুমন্তব্য থেকে একশতে একশ নিরাপদ নয়। যে তার সৃষ্টিকর্তার ব্যাপারে বাজে মন্তব্য করতে কুণ্ঠিত হয় না তার জন্মদাতা বাপ তো তার হাতের খেলনা মাত্র।।,0,religion
আল্লাহ এদের নেক হায়াত দান করুন।।।,0,religion
সালা মুর্খ মুনাফিক হাফিজুর,0,religion
এডমিন তুই ভন্ড।,0,religion
বন্ড দেওয়ান বাগী ফরিদ আটকে রসি এনায়েত পুরী সিরাজ গনজ এই পীর গোলু মারা গেলে মুখ দেখায় না দেখতে চাইলে পা দেখায়,0,religion
এসব ভন্ড গুলো অসংখ্য মুসলমানদ‌েরক‌ে মুশর‌েক বানাচ্ছ‌ে। তাদ‌ের মুখুশ উম্মুচন করার জন্য ত‌োমাদ‌ের অন‌েক ধন্যবাদ।,0,religion
তাহেরি ভন্ড,0,religion
আমি ইউটিউবে দেওয়ান বাগির কয়েকটা ভিডিও দেকলাম। সে নিজেকে নিয়ে বলেছে আল্লাহ বলে দাবিদার। আমিও সঠিক বিচার চাই,0,religion
এ‌দের আল্লাহ হেদা‌য়েত দান করুক। এই ভন্ড হুজুর দ্বারা ইসলাম যত ক্ষ‌তিগ্রস্থ হ‌চ্ছে কা‌ফেররা ও ততটুকু ক‌রে নাই।,0,religion
আমার পিও বক্তা জিহাদীহুজুর,0,religion
ধন্যবাদ তোমাকে,0,religion
এই চ্যানেল কে বলছি আপনি মিথ্যা একটি টাইটেল দিয়ে মানুষের মনে আগাত দিচ্ছেন কেন এই মঞ্চে আববাসি হুজুর কোন অপমানিত হননি,0,religion
শাহরিয়ার কবির খুশি কবির সুলতানা কামাল রাশেদ খান মেনন ডঃ জাফর ইকবাল এদের থেকে আমাদের সকল মুসলমানদের সাবধান থাকতে হবে,0,religion
আমার তো চিন্তা হয় এই নাস্তিকদের নিয়ে তারাতো জাহান্নামে যাবে তারা বুঝতে চাইচেনা আর প্লান করে নাস্তিক এক মুসলিম বসাইচে একসাথে আল্লাহ তাআালা মামুনুল হককে হায়াত বাড়িয়ে দিক এবং তাকে নাস্তিকদের সাথে লড়ার তৌফিক দিন আমিন।,0,religion
মইরা দ্যাখো,0,religion
দেওয়ানবাগি রে পাইলে আপনারা কি করতে পছন্দ করবেন??,0,religion
বাজনা টা না দিলে হয়না ভাইয়া,0,religion
কুততার বাচচা,0,religion
অামার প্রিয় বক্তা মিজানুর রহমান অাজহারি অাল্লাহপাক রাব্বুল অালামিন অাপনাকে নেক হায়াত দান করুক যেন বিশ্বের জমিনে ইসলাম প্রচার করে ইসলামকে অারও মজবুত করতে পারেন অামিন||||||||তাহেরি যে বন্ড সবার ধারনা হয়ে গেছে অাশা করি তার ভন্ডামির অবসান শীঘ্রই ঘটবে,0,religion
চার নাস্তিক এক সাথে যদি কথা বলে তাহলে কি করে একজন উওর দিবে কথা বলার সুযোক তো দিতে হবে,0,religion
এমন ভিডিও আরো চাই,0,religion
এই নাস্তিকদের বাপ যে কতজন তা ক্যালকুলেটর দিয়ে হিসাব করে পারবেন না সেজন্য ওরা নাস্তিক আল্লাহ ওদের ধংস করে দাও,0,religion
বুকে আয় ভাই,0,religion
জিকির দিলে সবগুলা বসেযেত,0,religion
ভাই দের মেহনত আল্লাহর তালা কবোল করোন,0,religion
শাজালালের কোন গাজাখোর পাইনি জারাগাজার নি য়তকরে তারাতো পাবেই,0,religion
যে বলে হাফিজুর রহমান ভনড সে মানুষ না।,0,religion
কুওা,0,religion
কত সহজ নাস্তিক বলা।,0,religion
ওই কি বোজে ওয়াজের মানুষ যে কেমন বক্তা আর খুজে পায় না,0,religion
অনেক অপেক্ষা ছিলাম।,0,religion
আল্লাহ তুমি এদের বিচার করুন,0,religion
মুসলমান দের পির এক জন মহানবী আর কেউ না ꫰,0,religion
তোর মত লেবাজধারী মানুষ শয়তানের দেওয়ানবাগী সম্পর্কে ধারনা হবে সে কে? তুই হলি আবু জেহেলের ন্যায় মূখ্য। যারা তোর কথা মত চলবে জীবনে সবচেয়ে বড় বোকামী করবে। কারণ তুই যে কাজটি করতেচিস সেটা কোন মানুষের কাজ না এটা হলো একটা আস্ত শয়তানের কাজ। তোর যে ভিডিও দেখলাম সম্পূর্ণ ভিডিওতে তোকে একটা আবাল বাছুর ছাড়া কিছুই মনে হয়নি। তোর ধর্ম সম্পর্কে যে জ্ঞান দেখলাম তা মনে করা হচ্ছে এক সমুদ্র পানির মধ্যে এক বিন্দু জলের কোটি ভাগেরও এক ভাগ নয়। অতএব এই সামান্য জ্ঞান নিয়ে একজন আল্লাহর বন্ধুর সমালোচনা শয়তান ছাড়া আর কারও হতে পারে না। তুই বলদ তার জন্য বলেচিস যারা বিদেশ থেকে এত টাকা খরচ করে দেওয়ানবাগীর কাছে আসে তারা ভুল করছে। আরে বলদ তুই যদি বুজদি তার কাছে কেন মানুষ আসে তাহা হলেতো হতোই। তারা আসে বছর পূর্বে যে ধর্মটা রাসুল পাক স রেখে গিয়েছিল তার স্বাদ গ্রহণ করতে। তোদের মতো নামধারী আলেমরা আজ মুখোশধারী প্রমাণ হচ্ছে আজ তোদের জন্য মসজিদে মাদ্রাসায় ছেলে মেয়ে বলাতকার হচ্ছে। তোদের ঈমান হলো লোক দেখানো তোদের মধ্যে আল্লাহ রাসুলের কোন প্রেম নাই। তোরা কারি কারি কিতাব পরিয়া নিজে নিজে মোসলমান হইয়াছ। মোসলমানের ঘরে জন্ম নিলেই মোসলমান হওয়া যায় আল্লাহ পাকের মনোনিত ব্যক্তির নিকট বাইয়াত হয়ে মুসলমান হতে হয়। রাসুল পাক স আসার পূর্বেও এরকম কিতাব ছিল না। মুসায়ী ধর্মের ঈসায়ী ধর্মের কিতাব ছিল না। তারপরও কেন রাসুল পাক স কে আসতে হলো। কারণ তোদের মত নামধারী মুসলমানরা ধর্মের ফতুয়া দিয়া আইয়ামে জাহেলিয়াতের যুগ সৃষ্টি করিয়াছিল। আজ রাসুলের ওফাতের পরে আর আহলে বায়েত তার নায়েবে রাসুলগণই সেই রাসুলের ধর্মটা তাদের সিনার মাঝে ধরিয়া রাখিয়াছে। আর যারা তার কাছে যাবে তারা অবশ্যই রাসুল পাকের সেই ধর্মের স্বাদ অবশ্যই পাবে। ইউটিউব ও ফেইসবুকের সহজ সরল বন্ধুরা ঐ লেবাজধারী আর কেহ নয় সে এই ভিডিও বানিয়ে ব্যবসা করছে। সহজ সরল মানুষদের বোকা বানাচ্ছে। একটা কথা চিন্তা করেন যুগে যুগে যত আল্লাহর বন্ধুগণ এসেছেন তাদের বিরুদ্ধে এক শ্রেণীর লোক উঠে পড়ে লেগেছে কিভাবে তারা অপমানিত করবেন লাঞ্চিত করবেন। মানুষদেরকে আল্লাহর বন্ধুর নিকট হইতে দূরে সরিয়ে রাখবেন। আপনারা ইউটিউবে দেওয়ানবাগীর অপপ্রচার ছাড়া অন্য যে সকল ভিডিও গুলো আছে সেগুলো দেখুন বুঝতে পারবেন সে কত বড় মাপের তাসাউফ বিজ্ঞানী ও আল্লাহ তত্ত্বের জ্ঞানী। তার কাছে মানুষ গেলে রাসুলের কাছে গিয়ে যে সকল শিক্ষা পেত তাই তার কাছে পাচ্ছে। তার কাছে গেলে তিনি শিক্ষা দেয় আত্মশুদ্ধি দিলজিন্দা নামাযে হুজুরী আশেকে রাসুল হওয়া। অতএব কাহারো কিছু শর্ট ভিডিও কাটিং করা তথ্য দেখিয়া কোন মন্তব্য করিবেন না। সকলকে ধন্যবাদ।,0,religion
কথা সুন্দর করে বলতে পারেনা,0,religion
মাশাল্লাহ ব্রো আমার রিকোয়েস্ট রাখার জন্য অসংখ্য ধন্যবাদ শুভকামনা রইল প্রিয় আপনার জন্য,0,religion
লেংটা করে পিটালেই ঠিক হবে।,0,religion
দেওয়ানবাগী কে ইয়াবা উদ্বার এর জন্য নেওয়া হউক । পুলিশ ।,0,religion
সাবাস বেটা চালিয়ে জাও আমরাই আছি থাকবো ইনশাআল্লাহ,0,religion
? গাঞ্জা হিরোইন ককটেল।,0,religion
আল্লাহ তুমি তাদেরকে হেদায়েত দান কর হেদায়েত না থাকলে ধবংস করিয়া দাও।।। আমিন,0,religion
গীবত করা হারাম। এই ব্যাটা কি,0,religion
? ? দেওয়ানবাগী স্বপ্নে আসছিল এদের নিশ্চয়ই,0,religion
কেমন জানি পরিচিত মনে হচ্ছে না??,0,religion
ওয়াজের মাঠ নাকি গালাগালির মাঠ? বেয়াদব হুজুর ভন্ড হুজুর শিন্নি হুজুর,0,religion
তাহেরির দালাল এই বসেন বসেন,0,religion
শালা তুই একটা বেয়াদব,0,religion
তোদের আমদানি কৃত গাজা ই ত মাজারে যাই,0,religion
এরা মারা গেলেও হুজুরের রা নাস্তিক ভেভেও জায়নামাজ দিবে য়,0,religion
দুনিয়াতে তর্ক করা যায় আখেরাতে নয় আল্লাহ আপনি সবাই কে হেদায়েত করেন আমিন।,0,religion
এই সব ভন্ডরা ইসলামের নাম খারাপ করতেছে,0,religion
অদের জাযগা হো জাহান্নাম,0,religion
ভাই ঠিক আছে পাসে আছি,0,religion
তাহসিনেশনের নকল পুরাদমে,0,religion
আজহারি নাম্বার ভন্ড,0,religion
শয়তানের ভাব দেখলে আর বাঁচিনা,0,religion
তালি দিসেন সবাই???তালি কিন্তু,0,religion
নাউজুবিল্লাহ। তুই কি আলেম?,0,religion
কী ক্ষতি করলো??,0,religion
মিরপুর এ শাহ আলী মাজারে বাবা গাজা খায়,0,religion
সবই টাকা আয় এর ধান্দা কাফের গুলা,0,religion
চরমোনাই এটা ঠিক হয়নি ওনি বনড না,0,religion
দুইটা থাপ্পর দিয়া আব্বার নাম ভুলিয়ে দেয়া ওহ্ চরম হইছে বস।,0,religion
হ্যাঁ এইটা সত্যি এই পীরের অন্ধ ভক্তদের আসলেই ব্রেইন নাই😂😂😂😂 পাগলের থেকে ও অধম😂😂😂😂,0,religion
সে আর বড় সইতান,0,religion
আহ হুজুর কে ধমকালো লোক্টা কিন্তু পাব্লিক যখন লোক্টাকে মারতে গেল তখনি আবার হুজুরি বল্লো সবাই বসেন সেলুট হুজুর,0,religion
হুজুরকে আল্লাহ নেক হায়াত দান করুন আমিন,0,religion
বক্তার উচিত কথায় মুর্তিপুজারীদের গা জ্বলে উঠছে।,0,religion
আল্লাহ তাদের হেদায়েত করেন,0,religion
হা হা হা হা হা হা,0,religion
এদের স্বচোক্ষে গুলি করে মারা উচিত,0,religion
এসব নাস্তিককে জুতা মারে স্ডেক থেকে বের করা উচিত,0,religion
শয়তান ভর করেছে,0,religion
ও যুবক কোটিপতি হতে চাও | | মিজানুর রহমান আজহারী,0,religion
ওয়াজ এর মধ্য কোন মাধুর্যতা নাই। ফাটা বাশের মত।,0,religion
ভাইয়া ভিডিওটা বানানোর জন্য আপনাকে অনেক ধন্যবাদ ওইসব দেওয়ানবাগী দের জুতা মারা দরকার,0,religion
টিক করতাচেন বাই,0,religion
আমি আপনাদেরকে ধন্যবাদ দিয়ে ছোট করতে চাই না। হাফিজুর রহমানকে হেদায়েত দান করেন জামিন।,0,religion
কত্তার মত মারার দরকদে,0,religion
ভন্ড কে দেখেন না দেখলেই তো বুঝা যায়,0,religion
আমি যদি দেশের কোন উচছ কমতায় থাকতাম তাহলে বাংলার মাটি থেকে নাস্তিক মুছে পেলতাম।।।,0,religion
সব নাস্তিক দল,0,religion
আল্লাহ এ দেশে নাস্তিক দের কোনো বিচার নাই আল্লাহ এ দের হেদায়েত দান করুন না হলে ধ্বংস করে দিন,0,religion
বেশী ভাগ লোক নারী লোভীর কারনে কাফের ও মুনাফেকের হয়। এসব ঐশিলতা বেহায়াপনার গানবাজনার। কারনে লোক শান্তির ধর্মের ত্যাগ করে কাফের হয়। অতিরিক্ত পচা কাম করার ফলে ঈমান বের হয়ে যাই তখন ইসলাম ধর্ম বিশ্বাস করে না।,0,religion
হায়রে ভন্ড তোর জন্ম জানি কোন নিষিদ্ধ পল্লিতে!!,0,religion
অসংখ্য ধন্যবাদ তাহসিন ভাই।।💓 এবার দেখুন দেওয়ানমাগির কিছু হাতে গোনা কিছু পালতু চামচা আছে তারা এতে উরাধুরা কপি পেস্ট আর গালিগালাজ করে।।যাইহোক আল্লার কাছে আপনার জন্য দোয়া করি।,0,religion
আমার দেখামতে মিরপুর মাজারে বেশি গাজা খাওয়া হয়ে,0,religion
ভাই আপনাকে লক্ষকোটি সালাম জানাই আপনি এই ভিডিও এর মাধ্যমে ভন্ডদের তুলে ধরায় অনেক মানুষের উপকার হবে।,0,religion
একমাত্র মৃত্যু দন্ডই এদের শাস্তি।,0,religion
নাস্তিক এর সাথে যারা একমত পোষণ করছিস তোদের জন্য কঠিন আযাব অপেক্ষা করতেছে।,0,religion
পুরো ভিডিও কে কে দেখছেন? আমি কিন্তু পুরো ভিডিও দেখছি।,0,religion
ভাই আপনার কথা গুলো ঠিক ভাই কিনতু একটু সাবধানে থাকবেন ভাই। আপনার। প্রতি আমাদের ভালোবাসা রইলো,0,religion
বাংলাদেস সরকার এগুলাকে। কিছু বলবেননা কারন বললে চেহার থাকবেনা সরকারের,0,religion
ভাই আপনার কসছে রিকোয়েস্ট ওই দেওয়ান বাগি কে আর কোনো বিডিয় তে আনবেন না ওর কথা সুইলে আমার মাথার রক্ত গরম হোয়ে যায়,0,religion
আমার ছোট সাহেবের মুখেও দাড়ি আছে ! তাই তো কামাই না!,0,religion
নাস্তিকদের যুক্তি খুবই দুর্বল।,0,religion
কাঠমোল্লাদের অত্যাচারে সাধারণ মানুষ বিরাট বিপাকে,0,religion
এইকথাগুলোসুনাহারাম,0,religion
পির ধরা ফরজ।আর ধরেই লাঠিপিটা শুরু করতে হবে।,0,religion
তাহেরী হলো আসল ভন্ড,0,religion
এই মিডিয়ার প্রথম হেডলাইনটা যে লিখেছে সে নাস্তিক আমরিকার দালাল,0,religion
বেয়াদব টা চেয়ারে বসে আছে আর গুরুজন সব নিচে বসে আছে আর কথা বলে কিভাবে ফাজিল যারা এ ধরনের শিশু বক্তা আনে ওদের মত মূর্খ একটাও নাই সালার বাংলাদেশ,0,religion
ভাই। যারা কমেন্টস করেছেন সকলেই ঠিক । কিন্তু বিষয়টি হলো এই রকম একটি অন্ধ লোক কে দুগ্ধের স্বাদ বুঝাতে গিয়ে বলা হচ্ছে দুধ খুব মজা । অন্ধ বলছে দুধ দেখতে কেমন? বলা হলো সাদা। অন্ধ বলছে সাদা কেমন? বলা হল বকের মতো । অন্ধ বলছে বক কেমন ? একটি কাস্তে এনে অন্ধের হাতে দিয়ে বলা হল কাস্তের মত । অন্ধ হাত বুলিয়ে বল্ল তোরা আমায় মারতে চাস? এই বাকা জিনিস খেলে আমিতো মরেই যাব ভাই বোঝার ভুল রূপক কিছু কথা উদাহরণ থাকে তাহা বোঝার জন্য মন থাকা চাই ।,0,religion
কুতার বাচা,0,religion
আমার সব চেয়ে প্রিয় আলেম হলেন মিজানুর রহমান আযহারী হুজুর?,0,religion
বাংলার সাহসি বক্তা,0,religion
সাধারণ জ্ঞান নেই তাহেরির,0,religion
আল্লাহ সবাইকে সঠিক পথে পরিচালিত করার তাওফীক এনায়েত করুন।,0,religion
চারটা কুকুড়,0,religion
এইটার ভম জন্যই এতোদিন অপেক্ষা করছিলাম অসংখ্য ধন্যবাদ,0,religion
এর বিচার চাই,0,religion
তুমি যাহাই কর সেটা একান্তই তোমার কর্ম তোমার কর্মফলের জন্য তুমি নিজেই দায়ী এবং এরফল ও তোমাকেই ভোগ করতে হবে ।সুতরাং তোমাদের এই অপ কর্মের সাক্ষী লক্ষ লক্ষ আল্লাহ এবং রসুল প্রেমী মানুষ বাঁচার কি কোন উপায় আছে ?একমাত্র তাওবায়ে নসুহা ছাড়া ?,0,religion
এটায় তয় পাগল হয়ছে😄😃😁😀😋,0,religion
এখানে যা দেখলাম মনে হচ্ছে ভিডিওটির কথা এডিট করা মানে সত্য প্রচার করা হয়নি,0,religion
চালিয়ে যান। আমি আছি।আপনারা ভন্ড আবু সুফিয়ান আল কাদেরী সম্পকে আরো ভিডিও দেন।তবে হকের পক্ষে থাকবেন,0,religion
শুধু ভন্ড হুজুর দের ভিডিও বানান কেন? ভালো কিছু আলেম দের নিয়ে ভিডিও বানান না কেন? এই নিয়ে আপনাকে তিন বার বললাম। কথা কানে যায় না?,0,religion
আল্লাহ এদেরকে হেদায়াত দেক নাহলে এদেরকে ধংস করেদেক আমিন,0,religion
এইসব পোলাপানদের মানুষ ওয়াজের জন্য ডাকে কেন বুজিনা,0,religion
আল্লাহ তুমি মামুনুল হক সাহেবকে নেক হায়াতদারাজ করিয় আর মানুষ রুপি ঐ জন কুকুর কে হেদায়াত কর,0,religion
লোকটা কিন্তু ঠিক কথা বলছে এটাতো ফতুয়ার মাহফিল না।তার উচিৎ ছিল কোরআন এবং হাদিস থেকে কথা বলা।কিন্তু সে মানুষের প্রশ্ন নিয়ে ফতুয়া বাজি করতেছে।,0,religion
ভাই সব ভালো লাগলো কিন্ত হাফিজুর রহমান সিদ্দিকির ছবি টা কেটে দিলে আমার কাছে মনে হয় ভালো হতো,0,religion
বস চালিয়ে জান👍,0,religion
এই এরা কি মুসলিম পরিবারে নেওয়া কোন মানুষের বাচ্চা নাকি অন্য কিছু?? আল্লাহ আলামিন তাদেরকে হেদায়েত দান করুন আমিন 💙🤗💙,0,religion
নাস্তিক নাস্তিক নাস্তিক নাস্তিক এরা ইসলামের শত্রু,0,religion
। তারা সামনে তার ছবি রাখে এই কারনে যে তারা জাতে পুরা নামাজ এ জাতে দুনিয়াবি চিন্তা না আসে শুধু আল্লাহর প্রতি ভক্তি আসে কারন তারা বিসশাস করে যে অনার ভিতর আল্লাহ আসে তাদের মতে এই যে যদি নামাজে দুনিয়াবি চিন্তা আসেও তাহলে ছবি তে তাকালে তারা আল্লাহ কে দেখে।আমি প্রত্তক্ষ্য সাক্ষী,0,religion
তাহেরীকে আওয়াজ মজা নেওয়ার জন্য শুনি শিক্ষার কিছুই নাই,0,religion
যারা কমেন্ট করেন তাদের দৃষ্টি আকর্ষন করে বলতেছি যে নবীর কলমা পরে আমরা মুসলমান হইলাম সে নবীর অক্ষর জ্ঞান ছিলনা যে নবীর হাদীস পড়ে মানুষ বড় আলেম হয় এখন নাকি সে নবী নিরক্ষর হয়ে গেছেন মানুষ কত বড় মূর্খ হলে এইরকম কথা বলতে পারে যে নবীর শানে একের পর এক বেয়াদবী করতেছে সে কিভাবে মানুষের প্রিয় বক্তা হয় যে কুরআন হাদীস পড়ে নবীর শান পায়না সে আবার কিসের বক্তা ? মহান আল্লাহ বলেন পৃথিবীর গাছকে যদি কলম বানানো হয় আর সাগরের পানিকে যদি কলমের কালী করা হয় জমিনকে যদি কাগজ বানানো হয় তার পর ও আমার হাবীবের শান বর্ণনা করে শেষ করা যাবেন। নিশ্চয় আযহারী একটা বলদ এতে কোন সন্দেহ হয়।,0,religion
আল্লাহ সকল হ্মমতার মালিক জাকে ভালু রাকবেন জাকে ভালু লাগবেনা তাকে রাকবেনা আল্লাহ র ছছা সকলে কে বুজার তৌফিক দান করুন আল্লা,0,religion
ফেরাঊনের চেয়ে ভয়ংকর ছিলো,0,religion
আল্লাহু আকবার।তুমি তাদের হেদায়েত দান করো।,0,religion
বসেন বসেন‌ বইসা যান এ কেমন জিকির 😂😂😂😂😂,0,religion
ফাসি চাই,0,religion
যে মানুষ গুলা ওনার মুরিদ তারা মনে হয় গাঁজা মদ হিরোইন সব খেয়ে ওয়াজ শুনতে বসে।,0,religion
সব গুলো কি পাগল নাকি কি বলে নিজে তো জানে না ওহহো ওহহো মানে কি,0,religion
অধিকাংশ মানুষ ইমান আনার পরও মুশরিক,0,religion
যারা গালি দিছেন তারা কথাটা ভালো করে বুজেন মাজারে গিয়ে মাজার ওয়ালার কাছেতো চাওয়া যায় একথা বলেনাই জয় বড় একটা শয়তান জয় কথাটা পেচাইতে চাইচিলো তাহেরি বলছে অলিদের মাজার জেয়ারত করা যাবে এবং তাদের উচিলা দিয়ে যেমন আল্লাহ আপনার এই মাহবুব বান্দার খাতিরে আমারে মাপ করে দাও এইভাবে বলা যাবে আর এই ভাবে বলি আমার আর এই ভাবে বললে কি আর মাজার ওয়ালার কাছে চাওয়া হয় নাকি,0,religion
বদমাশ তুই কে মানুষের কথা কে কিরম চলে সেটা নিয়ে বেস্ত তর মত বদমাশকে কেউ কি যাওয়ার জন্য বলে মানবতা খারাপ লুকিয়ে রাখা ভালো কে যা নিয়ে দেওয়া আমার নম্বর,0,religion
চট্টগ্রামের মানুষরা তো দেওয়ানবাগির প্রচুর ভক্ত😂😂😂।,0,religion
আল্লাহ তোমি এ মোনাফিকের বিচার করো,0,religion
এই চার নাস্তিককে জুতা পিটা করা দরকার,0,religion
আগের আলাপ বাদ দেন এখন কি বলে তা বলেন,0,religion
তোমাবে অনেক ধন্যবাদ,0,religion
এই ভন্ডের ফাশি হয় না কেন,0,religion
কি জানোছ তুই বেকুব।।,0,religion
আমি কনফিউজড! গাঞ্জা নাকি হিরোয়িন?😁,0,religion
একজন আলেমের সমালোচনা করার আগে নিজে সংশোধন হও,0,religion
আসসালামুআালাইকুম। ভাই দেওয়ান ভাগি কি এখনো বেচে আচে? যানাবেন,0,religion
তুমি তো ইচরে পাকা আবার ফেসবুকেও আইডি আছে,0,religion
হুজুর তাহেরি বন্ড শয়তান বাংলাদেশ সবাই জানে,0,religion
তাহেরির কে এ দেশ থেকে ভ্যান করে দেওয়া হোক।,0,religion
তিন মুর্খ কি বলে ইসলাম সমপর্কে তাদের কোন ইলম আছে।,0,religion
আল্লাহ বলেছেন যারা হক্কানী আলেমদের বিরুদ্ধে কথা বলেন তাদের নাকি জন্মের ঠিক নাই আমার তো মনে হয় তাই আজকে তোর মাকে গিয়ে জিজ্ঞেস করিস তুই কার সন্তান তুই কার সন্তান কারা কথা তোমায় বলতে পারে ভালো হয়ে যা তবা করে ফিরে আয় আয়,0,religion
কেন শায়ের করবো ।। আপনাদের নবী তো আর ইউটিউব ব্যবহার করতনা তাই ভিডিওটি শায়ের করলে পাপ হবে,0,religion
চার নাস্তিক কি করবে মরার পরে।,0,religion
দেওয়ানবাগী হুজুরের বিরুদ্ধে মিথ্যা বানোয়াট অভিযোগ এনে যারা এই হিরো সাজতে চেয়েছে তারা সাবাই আজ জিরো তুই নিজেই আবার রোষ্ট হয়ে যাইস না ফকিন্নির পুত,0,religion
ঐ খবিশ লালশালু পড়ে মাজারপুজারি গূলি হিন্দূদের মতন লাল শালু পড়েছে ঐ লাল কাপড় কি নবী স এর কি নমুনা বাহ সুনাত তরিকা ভন্ড মাজারিরে জুতাপিটা করে ঐ ইষ্টেজ থেকে নামানো উছিত,0,religion
আপনার কথা রাইট পাগল না বুজে পাগলামি করলে আপনার কিছু আসে জায় না,0,religion
এতোদিন জানতাম হাফিজুর রহমান হুজুর কিছু গেয়ান রাখেন কিন্তু বিদাদ কি সেটাই বুঝেনা,0,religion
আলেম ভাই কে বলছি এই সব নাস্তিকদের সাথে বহিস্থে এই সব উনষটানে যাবে না,0,religion
ইমাম বুখারী সম্পর্কে ওর ধারণা আছে??? ও বোখারী শরীফকে নিয়ে মন্তব্য করে।,0,religion
ডিজে জিকির করেন ভন্ড,0,religion
তাহেরি পাইকারি খায় তাই আবল তাবল কয়,0,religion
পিপীলিকার ডানা গজায় মরিবার তরে ! আল্লাহ যেন এই সব কাফের দের হেদায়েত না দেয়,0,religion
যারা দেওয়ানবাগী হুজুরের বিরোধিদা করে তারা সাবধান হন ধংস হবে তারা কারন বর্তমান যুগের ইমাম অলিদের বাদশা সৃফি সম্রাট দেওয়ান বাগী হুজুর কেবলাজান,0,religion
জুতাদিয়া পিটাইয়া ইস্টেজ থেকে নামায়া দেওয়া দরকার ছিলো,0,religion
ভাই হের পেডে কয়ডা বচ্চা?,0,religion
ওরে আর কিছু বলার নাই।ওরে যদি আল্লাহ হেদায়েত দেয়!,0,religion
কী ভাবরে বাবাহ!!,0,religion
এইসব ভন্ড পিড়দের ভরা মজলিসে ল্যাংটা করে ছিবটির ঠাইল দিয়ে বেত্রাগাত করতে করতে মেরে ফেলা উচিত। আর ভাই তোমাদেরকে আমার মন থেকে অশেষ ধণ্যবাদ এরকম দৃশ্য সবার মাঝে তুলে ধরার জন্য। আর আমি চেষ্টা করব তাদের বিরুদ্ধে রুখে দাড়ানোর জন্য। হে আল্লাহ ভন্ড পিড়দের হাত থেকে দেশটা বাচিয়ে দিন।,0,religion
দেওয়ান বাগী ভন্ড।মানুষ রুপী শয়তান,0,religion
সালের মুরগী সাপলায়ার মুরগী কবির,0,religion
চাঁদের বুকে তার ছবি তো আমি দেখলাম না। আমি তো কানা না।,0,religion
তাহারী একটা পাগল,0,religion
এখানের সবাইকে বন্ডবলা ঠিক হবেনা।,0,religion
সবাই রিপোর্ট মারো এই মিডিয়া কে,0,religion
তোই ওয়াজ করলি না। শুধু গীবত করলি তোই কোথায় ভাল।,0,religion
বড়ন,0,religion
এই হুজুর বেদাত বেদাত বলে জাইতেছ কতো মানুষ যে বেনামাজী চিন্তা আছে তোমাদের কাছে ?,0,religion
আপনারা এগিয়ে যান লাড়াই চালিয়ে যান ভন্ডদের বিরুদ্ধে।,0,religion
ভাই মুসলমান এর মধ্যো বিভেদ সৃষ্টি না করে ভালো কিছু করেন জাতির উপকার হবে,0,religion
মুরগি চুর,0,religion
ধ্বংস হোক সয়তানটা,0,religion
গাড়ি উড়োজাহাজ আর হেলিকপটার তো খিরিসটানরা বানাইসে তাইলে ভন্ড হাফিজুর তা কেন চড়েন !! অসভ্ভো ভন্ড কোথাকার,0,religion
হুজুরের কথা সটিক,0,religion
শিশু বক্তা জামান বড় একটি ফেতনা!!!!,0,religion
দেওয়ান বাগী কাফের,0,religion
এনায়েত এমনিতেই দাজ্জাল ও অপমান আর মান কি আর আছে দেখলাম্না ভিডিও টা,0,religion
আহমদ শফি সাহেব ভন্ড !!!!!!!!!!,0,religion
এরা কেউ হুজুরকে কথা শেষ করতে দিচ্ছে। কম যেনে কথা বললে যা হয়।,0,religion
নতুন কাফের বাচ্চাই সুন্নিওতের দুশমন ওলীদের দুশমন আইছে।,0,religion
আললাহ তুমি এর বিচার কর ।।।।,0,religion
নাস্তিক লোপাকে করা বাশ দেয়া হইছে,0,religion
ভন্ড পীরদের ভন্ড পীরদের,0,religion
আপনি তার সম্পর্কে কতটুকু জানেন না জেনে একজনকে ভন্ড বলা ঠিক না তার স্ত্রীর ছবি একটা দেখে তাকে ভন্ড বলতেছেন ছবিটা কিভাবে আসছে কোথা থেকে আসছে সেটা কি জানেন,0,religion
হুজুরের আযান আমাকে পাগলপাড়া করে দিয়েছে সুবহানআল্লাহ কি মধুমাখা কন্ঠ আল্লাহ উনাকে এইভাবে সবার মাঝে কুরআন বানী পৌছে দেয়ার তৌফিক দান করুন।,0,religion
তুমি ওয়াজ করতে আইছো ওয়াজ করো,0,religion
কি বলবো?,0,religion
ভন্ড দেওয়ানবাগী সালারে জুতা পেটা করা হোক,0,religion
আরে ভাই তুমি কি এই ভুল গোলা না ধরে যেগুলি শুনলে মানুষ হেদায়েত হবে সেই গুলি দেখাও বুছ,0,religion
বাংলার বাবা একটাও বাদ দেইনি🤣😂🤣😂 তাহেরি সাহেবের এতো বাবা কেম্নে হইল রে ভাই?🤣😂,0,religion
পির বলতে কিছু নাই। সব গুলা ভন্ড ব্যবসায়ী,0,religion
ইসলাম বিদ্দেশি নাস্তিক মূর্তাদরা কি করে ইসলামের ও হাদীসের কথা মানবে।,0,religion
এই জিলানি নিম বাড়ি এক মসজিদে ইমামতি করিয়া এক লােকের বউয়ের সাথে প্রেম করিয়া দরা খাইয়া গেছে,0,religion
চার নাস্তিক দের জুতা দিয়া পিটানো দরকার,0,religion
দারুন এপিসোড তে আসুন আমরা ভন্ড পীর বর্জন করি।,0,religion
শিশু বক্তা কেয়ামতের আলামত মিজানুর রহমান আজাহারি ্জুতা পিঠা করে মাহফিল হইতে ভাইর করে দেওয়া উচিৎ। কারন গিবত ছাড়া আর কিছু জানে না,0,religion
অদের কে জুতা দিয়ে পিঢাও না কেনো🇧🇩🇸🇦,0,religion
বলদের বাচ্ছা হাদিসের সনতটা কতটুকু সহি জানসনি। হাদিসের রাবি কে বলদ ছাগলের মত চিল্লাস আর জাল হাদিস প্রাচার করছ মিছুউয়াক করা সুন্নত তুই সে সুন্নতকে ঠাট্টা করলি,0,religion
আসছালামু আলাইকুম ডাঃ জাকির নায়েক আপনার কাছে একটি অনুরোধ এই নাম্বারে ফোন দিন অল্প সময় কথা বলবো,0,religion
ইয়া আল্লাহ ইফতারের সময় দোয়া কবুলের সময় এই সময় দোয়া করতেছি ভন্ড পীরদের হোদায়ত দান কর এবং তাদের হাত থেকে আমারদের হেফাজত দান কর। আমীন,0,religion
দেওয়ান বাগীকে কতল করতে হবে,0,religion
আল্লাহ তাদেরই হেদায়ত করুক,0,religion
নাস্তিক দের কে জুতা পিঠানো দরকার।,0,religion
কার সাথে কারে মিলায় কোথায় আজারি কোথায় তাহেরি কোথায় গাচতলা আর কোথায় চাদের তলা আর কিচু বললাম না,0,religion
সাইটে মাজার পুজারিকে কান ধরে উঠে দেওয়া হক,0,religion
অাহলে হাদিস অাহলে শয়তান অরে শয়তান তুই কার সাথে কাকে মিলাছ,0,religion
কাল কেয়ামতের দিন নবীকরীম সঃ ব্যাতীত সবাই বলবে ইয়া নাফসী সেখানে তোর খাজা বাবা কি করবে শয়তানের দল।,0,religion
ফাযিল পর্যন্ত লিখাপড়া করে ফাজলামি এর উপর উচ্চ শিক্ষা লাভ করে এক বড় আকারের ফাজিল হয়। এই কথাগুলো তে কি ফাযিল শিক্ষা কে অফেন্ড করা হচ্ছে না?আশা করি নেক্সট ভিডিও গুলোতে খেয়াল রাখবেন বিষয় গুলো।,0,religion
মুরগী কবির তোর মেয়ে কে পুটকি,0,religion
এই সব জাগায় যাওয়া হারাম,0,religion
নাউযুবিল্লাহ কাফেরের বাপ,0,religion
বাড়ার মাথা বলো,0,religion
আল্লাহ ওদের হেদায়েত দাও আর নাহলে আমার হাতে ওদের করার তৌফিক দাউ,0,religion
বেটা তুই এখন আলেম পাশ করোছ নাই আবার ফতোয়া দেছ। বেয়াদব,0,religion
মিজানুর রহমান আজহারী অত্যন্ত গেযানী ব্যাকতি,0,religion
অই বেটা বক্তা চুল কামাইয়া আয় ওয়াজে,0,religion
আল্লাহ আপনাদের সাহস বাড়িয়ে দিকওআরও এমন নতুন ভিডিও বানানোর তৌফিক দিক,0,religion
ভাই এই ভন্ড দেউয়া মারা বাগিরে আজ প্রথম আপনার ভিডিও তে দেখলাম 😂 নাউজুবিল্লাহ নাউজুবিল্লাহ এত্ত টা মিথ্যা বলে গাজা সে দেউয়ান খায়নাই খাইছে পাবলিক এই দেউয়ানের বক্তব্য শোনে ছি ছি দেউয়ান হচ্ছে সেফু 😤,0,religion
আমির হামজা কে আল্লাহ হায়াত দান করুন,0,religion
আল্লাহ নাস্তিকদের শাস্তি দেবে,0,religion
ওরে গুলি করে মারা উচিৎ বলে আমি মনে করি,0,religion
ইসলামকে অপমান করছে এই নাস্তিক।,0,religion
আপনাকে এসব কথা তুলে দরার জন্য,0,religion
সালালে জুতা মারবো,0,religion
সঠিক কথা বন্ধু,0,religion
আর এই ভন্ডরাই এখন মিজানুর রহমান আযহারীর বিরুদ্ধে লেগেছে।,0,religion
আচতাগফিরুললাহ।,0,religion
ঠিক বলছেন আমির হামজা,0,religion
শিশু বক্তা কিয়ামতের আলামত,0,religion
আপনে কি বলতে চান কুরআন দুনিয়র আবিশকার হুম,0,religion
তোদের জবাই করতে পারতাম,0,religion
আইমানের রোস্ট টা ভাল হয় নি। টাকা খাইচে তাহসিন।,0,religion
ছিছি,0,religion
শালা বন্ড়,0,religion
এই দেওয়ানবাগীর হুজুরের জুতা পিটা করে মেরে ফেলা দরকার সরকারের উচিত এসব ভন্ডদের ফাসি বা জেল দেওয়া,0,religion
এভাবেতো ভিখখা করে,0,religion
আল্লাহ আমাদের সবাইকে হেফাযত করেন,0,religion
দেওয়ানবাগী ভন্ড থেকে জুতাপেটা করা হোক,0,religion
বাংলার জমিনে সিহং পুরুষ হলেন আমির হামজা,0,religion
নাস্তিকের বাচ্চার সাহস হইলো কিভাবে হুজুরের গায়ে হাত দেয়ার,0,religion
আজেবাজে থামনিল করে নিজেকে পশুর কাতারে শামিল করবেননা এ দেশে ইসলাম কে ধংশ করছে আত্রসি চরমনা হেফাজত সঠিক ইসলাম এরা জানে মাগার বলতে চাইনা বরং বিভাজন তইরি করে আল্লাহ আলেম দেরকে এক করেদিন,0,religion
মুফতি আমির হামজা সত্যিকারের একজন কোরআনের সৈনিক,0,religion
ভাইয ভিডিও করলে হবে না এদেরকে বাংলাদেশ চারাতে হবে????,0,religion
নাউজুবিল্লাহ কি সব হচ্ছে এগুলো আল্লাহ তুমি তাদের হেদায়েত দান করো,0,religion
আল্লাহর কুরানকে যাঁরা উকমান করে তাদেরকে আললাহ দুনিয়াতে ও শাস্তি দেবেন আবার আখিরাতে ও শাস্তি দেবেন,0,religion
আমি যদি সে খানে থাকতাম তোরে জুতা মারতাম,0,religion
এগুলো এখনো দুনিয়ায় কেন আছে ধ্বংস করে দেওয়া হউক।।।,0,religion
সব গুলাই নাস্তিক।,0,religion
তোরেডা!,0,religion
শালা মুফতি গিয়াস উদ্দিন তাহেরী তুই কেমন পীর সাহেব তোর মাথায় এত বড় বড় চুল কেন আর তুই মেয়ে মানুষের মত মেকআপ করো কেন আরে পীর সাহেবদের চেহারাতে আল্লাহপাক এমনিতেই নূরানী বানিয়ে রাখে তারপর মেকআপ করালাগে কেন,0,religion
আল্লাহ তুমি মাফ কর এ নাস্তিকদের হেদায়েত দান করুন আমীন,0,religion
মানুষ রুপের তিন পশু দেখলাম,0,religion
হুজুরের কথাটা সত্য সত্যিই তারা পীর অলী আউলিয়া কোরআনের দাওয়াত দিতে এসেছিলেন,0,religion
মহিলাদের ক্ষেত্রেও কি সেইম ভাবে টিপ দিবে 😂,0,religion
ভাই শুধু চরমোনাই খারাপ নাকি? জানাবেন,0,religion
মুরগি চোরার বর কথা,0,religion
মুর্খ হারাম জার্দা,0,religion
আস্তাগফিরুল্লাহ আমি কি দেখলাম। নাওজবিল্লাহ,0,religion
কি বলব তোমাকে তাহেরী হুজুরের গোলাম হওয়া যোগ্যতাও তোমার নাই আর তুমি তার বদনাম করতেছেছ গীবত করা তো হারাম তাহলে তুমি কেন এখন গীবত করতেছ পুরোটাই সুনলাম গীবত ছাড়া তো কিছু কর নাই আর তোমার যদি এতই এলেম থেকে থাকে তাহলে তার সাথে সরাসরি বহস কর দেখি তোমার কত পাওয়ার আছে,0,religion
অপেক্ষায় ছিলাম এই রোস্টের জন্যে ধন্যবাদ তাহসিনেশন ❤,0,religion
এগুলোকে জুতা দিয়ে পিটা দেওয়া দরকার তবে তিন নম্বর জিকির জেটাকে ডিগবাজি বলছেন সেটার ভিতর কোন সমস্সা নেই কারন আল্লাহর জিকির করতে করতে অনেক সময় মানুষের মাথা ঠিক থাকেনা তাই এমন করে আসা করি বুস্তে পারছেন,0,religion
আমির হামজার সাতেআমিআচি,0,religion
ভালো ছিল এটা,0,religion
কিসের রক্ত দিয়ে তৈরি হয়েছিল এই মোটা কুকুরের মতোই মোরবি আল্লাহতায়ালা কবুল করিয়া নিন আমিন৷,0,religion
এটা কোন জাগায় ঘটেছে,0,religion
ভাই সময়ে সময়ে বলতে হয়।ভাই এটা হুজুরের ভুল মানি। তাই বলে আববাসি হুজুরকে। এমন বলবেন কেন।,0,religion
নাস্তিকের মাইরে বাপ,0,religion
এগুলা ভিডিও বানানোর সাথে সাথে তোমাদের আমল করতে হবে সব সময় ভালো করার চেষ্টা করবে এমন না যে আমরা ভালো ভালো ভিডিও বানাইতাছি যাতে আমাদেরকে মানুষের উৎসাহিত করে আর এটা বলতে হবে যে দেওয়ানবাগী কাফের,0,religion
মডেলিকং করলে তাহেরি সাব সাকিবকেও ফেল করাতো।,0,religion
আল্লাহ ভন্ড তাহেরিকে হেদায়াত দান করুক আমিন।,0,religion
মাজার পূজারী উন্মাদ পাগল😤😤😤,0,religion
আল্লাহ তাদের কে হেদায়েত করেন।,0,religion
জিকিরের চারটি শব্দ আছে সুবহানাল্লাহ আলহামদুলিল্লাহ লাইলাহা ইল্লাল্লাহু আল্লাহু আকবার আমার প্রশ্ন আপনি এগুলো নিয়ে জিকির করেন না কেন উল্টো পাল্টা কথা বলে ইসলামকে ধংশ করছেন ইয়ালি বাবা শাহআলি বাবা গোলাপশাহ বাবা এগুলো কি কোরআানে আছে নাম যদি থাকে আমাকে বলুন আল্লাহ তুমি আমির হামজাকে হক কথা বলার তৌফিক দান কর আর আমির ভাইকে হেফাজত করো,0,religion
খুব ভালো লাগলো ভাই। আপনি প্রথমেই সালাম দিয়ে শুরু করলেন। অনেক ধন্যবাদ 💞,0,religion
হুজুরেরা প্যামান ছারা কথা বলে না,0,religion
শায়খ হল বাঘ আর মামুন সাহেব সেই বাঘের বাচ্চা। অতএব এই নাস্তিকদের কোন টাইম নাই।,0,religion
সব নিউজ পরটাল গুলা সাওয়ার বেটা,0,religion
যেই দিন আমি এই নাস্তিক দের সামনে পাব। সেই দিনেই বোঝাব এদের কত দানে কত চাল।,0,religion
মাশাআললাহ হুজুর অনেক টেলেনট আল্লাহ সবাইকে হেদায়েত দান করেন,0,religion
এই শব শিশু আখোন ওয়াছ করে এদের আখোন শিক্ষার শুমাই,0,religion
আমি অবাক হয়ে যাই মুসলমানদের দেশে এরকম কাফের মুশরিকদের জায়গা কেমনে হয়,0,religion
আল্লাহ্ জ্ঞান দাও এদের,0,religion
অনেকে অনেক কিছু কপি করে ভাই তুই তো বলার ভঙ্গিমাও কপি করে ফেলেছিস। গুড যব। নতুন কিছু করে দেখা ভালো সাপোর্ট পাবি। ?,0,religion
এ বলদ যে কত বড় বলদ😠😠 আল্লাহ তারে হেদায়াত দান করুন,0,religion
এই মাহফিল টা চাঁদপুরে কোন জায়গায় হইছে?????,0,religion
বেশি বাল পাকনা গীরি না দেখাইলেই ভালো আরেকজনে ওয়াজে কি করলো না করলো সেই গুলা নিয়া তোমারে ওয়াজে আইজা বিচার বিশ্লষন করার জন্য তোমারে আনে নাই বলদ কোথাকার তোর ওয়াজ তুই কর বলদ কোতাকার,0,religion
আমার পছন্দ আজহারী হুজুকে।,0,religion
বিয়াদব 👎😡,0,religion
আল্লাহ তুমি আমাদেরকে হেদায়েত দান করো আমিন,0,religion
হুশিয়ার তাহেরী,0,religion
ভাই আপনার হয়ে গেলাম।,0,religion
এ আল্লাহ তুমি এ দের বিচার করো,0,religion
তুমি কুন জুজ্ঞতায় ওয়ায করতেচ বাবা,0,religion
তাহের একটা ভন্ড বদমাইশ শালা নিজেকে পীর মনে করে,0,religion
কি আর বলবো বলার কিছু নাই এসব দেখে,0,religion
যাঁরা দেওয়ানবাগীকে কাফের মনে করো তারা লাইক দেও,0,religion
এখনো সময় আছে ভালো হয়ে যা শয়তান,0,religion
আচ্চা ভাই এদের চেহারাটা এত বিকৃত কেন?? এত ভয়ানক চেহারা কেন???,0,religion
আলহামদুলিল্লাহ আপনাকে অনেক অনেক ধন্যবাদ,0,religion
আপনার ভিডিও এর জন্যে ধন্যবাদ,0,religion
হাফিজুর রহমানকে যে ভন্ড বলবে তার কোন ঈমান নাই নতুন করে আবার ক্যালেমা পড়ে মুসলমান হতে হবে সালাদের কোনো কাজ নাই শুধু আল্লাহ্ওলাদের বিরুদ্ধে কথা বলা,0,religion
আসসালামু আলাইকুম ভন্ড তাহেরিকে বাতিল করুন,0,religion
হাজার সালাম আপনাকে,0,religion
এরা ইহুদী খৃস্টান দের দালাল আমাদের দেশে ফেতনা তৈরি করছে,0,religion
আপনি এই সব বিষয় নিয়ে কথা বলার সময় কিছু আলেম ওলামার সহায়তা নিলে ভালো হয় । ওনারা ব্যাপার গুলা বিস্তারিত মানুষ কে বলতে পারবে । বিশেষ করে হাদিসের ভুল ব্যখা বিষয় গুলা নিয়ে ।,0,religion
তোমার সেটার মধ্যে এত চেতকে মুরুব্বী তো ভালো কথা বলছে,0,religion
কেয়ামত তো অনেক নিকটে এসে গেছে,0,religion
আস্তাগফিরুলা😪😪😪😪😪😪😪😪😪😪😪😪😪😪😪😪😪😪😪😪😪😪😪😪😪😪😪,0,religion
তুই বেডা আর বালো হইতে না,0,religion
চারজন নাস্তিক,0,religion
এই লুচ্ছা হুজুরগুলোকে মুকি এবং পাচাই লাতি মেরে দেশ থেকে তাড়িয়ে দেওয়া উচিৎ,0,religion
কুত্তাটা কে ফাঁসী দাও,0,religion
গিয়াসউদ্দিন কে এলাকায় খবর দিয়ে এনে মলম লাগায়ে দেওয়া লাগবো🤬,0,religion
এই সব হুজুর কে পিটিয়ে বের করা দরকার,0,religion
মহিলার মাথার চুল দেখে মনে হয় বৈশাখ মাসের খেরের পালা যা গরুকে খাওয়ানো হয়,0,religion
হুজুর টিক বলেছেন,0,religion
অাল্লাহ তুমি সকল মাুষের কে হেদায়েদ করুণ,0,religion
আমি তাহেরি র পুরো ওয়াজ টা সুনেছি কুনো ভুল দেখি নাই,0,religion
যে হুজুরদের কে ভালো লাগত তাদের কিছু কথা শুনে মনেয় হয় তাদের কে শয়তানে দোখা দেয়,0,religion
গায়ে আগুন দিওয়া উচিত,0,religion
আল্লা এই নাস্তিকের সঠিক পথে নিয়ে এসো আমিন,0,religion
যে উপস্থাপিকা তাইও আরো বড় নাস্তিক।।,0,religion
আল্লাহ্ তুমি এই লোক গুলো কে হেদায়েত দেও,0,religion
মিজানুর টে মুনাফিক,0,religion
বলদ,0,religion
কেয়ামতের আলামত অগুলো বড় বড় দাড়ী রেখে কপালে দাগ ফেলে বিরাট জূব্বা পরে নামাজ পড়বে এই ধরনের লোকদের আজকাল বেশী দেখা যায় এরা আবার বিরাট জ্ঞানের অধিকারী এদের সাথে ইসলাম ধরম নিয়ে কথা বলাই মুশকিল এইখানে এইরকম কতগুলো ভন্ড আলেম দেখলাম এদের দারা হেদায়েততো দূরে থাক শয়তানও এদের ভয় পাবে,0,religion
সালা গাবগাছি চোর,0,religion
ভন্ডামী ছাড়াও,0,religion
দেওয়ানবাগীরে বিচির নিচে একটা ইট রেখে যদি আর একটা ইট দিয়ে বারি দিয়ে থেতলা করে দিতে পারতাম । তবুও মিনে হয় শান্তি পাব না।,0,religion
ভাই তুমি সেরা! আরো আরো রেসিপি নিয়ে এসো ক্ষুধার্ত আমরা,0,religion
সুন্দর কথা বলেছে হুজুর,0,religion
বাতিলদের যেখানেই পাবেন সেখানেই আটকাতে হবে। যাতে বাতিল বেসি বারতে পারবেনা,0,religion
পাগল হুজুর,0,religion
ভন্ড আাযারি,0,religion
এই ভন্ড জানোয়ারের কয়েকজন মুরিদের সাথে অনেকবার ঝগড়া করেছি। বুঝানোই যায় না এসব আবালদের। আল্লাহ মাফ করুক এদের।,0,religion
সাবাশ ছোট ভাইয়েরা এইসব ভন্ডের আরো সায়েস্তা করতে হবে,0,religion
চার কুসন্তনের সাথে এক সুসন্তান আল্লামা মামুনুল হক দাঃবাঃ,0,religion
কতা কস একবার গালি খাছ হাজার বার,0,religion
ভাই ওদের টাকা বেশি হয়েগেছে 😡😡,0,religion
মিজানুর রহমান আমাদের গরব,0,religion
আল্লাহ জিবন কিয়ামত,0,religion
চালিয়ে যান ভাইয়েরা আপনাদের সাথে আল্লাহ্‌ আছে।,0,religion
ওরে কেও জুতা দিয়া পিডায় না কে,0,religion
আমাদের সবাইকে আল্লাহ হেফাজত করুন,0,religion
নায়েক সত্যি বলছে,0,religion
তাহেরী ভন্ড না বরং যারা কটছ তারা ভন্ড ওহাবী ভন্ড,0,religion
কার কাছে কত রকম জুতা আছে? তা দিয়ে তাহেরিকে মারেন! 👢👡👠👟👞। তাহেরিকে কুকুরে কামর মারক।🐕🐕🐕🐕🐕,0,religion
💜💜💜💜💜💜💜 ভাই আমরা আপনার পাশে আছি💜💜💜💜,0,religion
খেয়ে দেয়ে কোন কাজ নাই আই কাজ করবা আমার সাথে শালা ভন্ড পীর,0,religion
পরা ডিজে জিকির,0,religion
হের জন্মের ঠিক নাই,0,religion
হাফিজুর রহমান ছাড়া সবগুলো ভন্ড আহলে খবিস,0,religion
তোরা বিদেশে গিয়ে এতকিছু বলছিস একটু এই দেশের দিকে এসে বল তোদের কিকরি সালা কাফের দের দালাল,0,religion
এই চারটাকে আমার কাছে দিন মেরে ফেলব,0,religion
দেওয়ানবাগীর মুরীদ রা কই সামনে আয়,0,religion
কসম আল্লাহর আমি অনেক হাসলাম। আসলে তাদের মাথায় কি? আমার বুঝে আসেনা। এগুলোর নাম জিকির???,0,religion
তার কথা শুনে মনডা চাইছে আধাঘন্টা তারে জুতা দিয়ে পিডাই👞👞,0,religion
সালা এতো বড় ভনড ।সালারে জুতা পিটা দরকা ।তোর দোজগেও জায়গা হবে কিনা সেটাই ভাবছি ।,0,religion
এটাতো হাদীস ও কোরানে নাই কিন্তূ তাহিরি পাইল কই,0,religion
দেওয়ানবাগী কে আপনি বৎস ধরিয়া মৎস বেচিয়া গঞ্জে অকুলে কুঞ্জে না খাইয়া তাজা গরমের দিনে ভক্ষন করিয়াছেন মেয়াদ উত্তীর্ণ গাজা !!!!😂😂😂😂,0,religion
যে দেশে মুসলিম সে দেশে এ সব নাস্তিক অনায়াসে ইসলামের বিরুদ্ধে কথা বলছে আর জাতি তা সাদরে গ্রহণ করছে এটা সত্যিই লজ্জা জনক,0,religion
এক পক্ষে চার বদমাইশ ও নাস্তিক অপরপক্ষে আল্লামা মামুনুল হক এবং সাথে আল্লাহ আছেন,0,religion
এই রকম লোকদেরকে বাসদিয়ে পেটানোর দরকার ভন্ড,0,religion
তাহসিনেশন এর যদি ভালো কোনো ভিডিও থেকে থাকে তাহলে এই ভিডিওটাই।,0,religion
অনেক অনেক ধন্যবাদ ভাই,0,religion
সান্ত তোমাকে আল্লাহ তালা সুস্থ রাখুন এই দোয়া করি আর কোন দল এদের কিছু বলেনা কারন এরা র্পাটি ফান্ড ডোনেশন করে তাই এদের কে কিছু বলেনা আল্লাহ তালা আমাদের দেশের সমস্ত মাজার পির পুজারিদের হেদায়েত দেক এই দোয়া করি। আর সান্ত ওয়াক্ত নামাজ পরার চেস্টা কইর ভাল থাক।,0,religion
এই নাস্তিক গুলোকে শাহাবাগে বেঁধে জুতা মারা দরকার। এক গুয়েমি বেয়াদব।,0,religion
ওটা কে ওপোমান বলেনি পাগল এটা একটা মুনাফেকি পোস্ট তোর চেনেল আগে বাড় বেনি আমি তো ছিলাম ওখানে ওটা অপোমান নন,0,religion
পির মানেই সেখানে সমস্যা আছে।,0,religion
দেওয়ানবাগীর মাথা তার শরীর থেকে আলাদা করতে চায় তাহলে লাইক দিন।,0,religion
হায়রে ভন্ড যাত্রা পালাতে নাইকা শিল্পীদের এবাভে টাকা চিটানো বিলানো হয়,0,religion
সালা ওয়াস করেনা মানুসের সমালচনা করতে বইছে,0,religion
ঠিক আছে।আব্বাসি সবাইকে কাফের বলে এখন ওনি নিজে তো অপমান খেলো সালা সবাইকে কাফের বলে,0,religion
এদের কে যদি রাস্তা পেলেই পিটাইত,0,religion
আওয়ামিলীগ যে একটা নাস্তিক টিম সেটা সবার প্রমান হয়েছে,0,religion
তাহেরী বলেন৷ বুজলে বুজ পাতা না বুজলে তেছ পাতা,0,religion
পাগলে কিনা বলে ছাগলে কিনা খায় ভন্ড তাহেরি,0,religion
আপনাকে অনেক অনেক ধন্যবাদ ভাইয়া আপনাদের অনুষ্ঠান অনেক আনন্দ দিল অনেক কিছু শিখার আছে শিখে নিলাম,0,religion
আরে সাব নবী ও ওলিদের উসিলায় অনেক দূয়া কবুল হয় ওলিদের মাজরে তো আল্লাহর কাছে চাওয়ার কথা বলসেন তাহেরী সাব,0,religion
আমি মনে করি এইসব নাস্তিকদেরকে জুতাপেটা করা উচিত এদের পৃথিবীতে বেঁচে থাকার কোন অধিকার নাই,0,religion
এই মাহফাইল সবাই ব্যাশা এরা গাজা গেয়ে নাচতাচেএ,0,religion
মিজানুর রহমান কাফের,0,religion
এই সব ভন্ড্র দের কে জুতা মারা উচিত আর ইট পাথরের আঘাত করে কুকুর কে,0,religion
এই গুলো এডিট করা ভিডিও মানুষ নামের জানোয়ারের কাজ মূলত অনলাইনে আয় করার জন্য এগুলো তৈরি করা হয়।,0,religion
মিডিয়াকে সাবধান করতে করতেছি।।।,0,religion
মসলমানরাই সব সময় নাসিতক হয় 😏😏😏😏,0,religion
মাজার পুজারীদের জুতার মালা পরিয়ে রাস্তায় ছেড়ে দেওয়া উচিৎ,0,religion
জুতা দিয়া পিটানো দরকার তাহলে ভন্ডামির ভুত মাথা থেকে নেমে জাবে বেজন্মের ভন্ডোপির,0,religion
আমি ঐ মেয়ের ফাঁসি চাই,0,religion
একআয়াত কোরআনপরতেদিলে দাতভেংগেজাবে তুমিকিবুজো হালাল আর হারাম,0,religion
মামুনল হক হুজুর আছে বলেই লাইক দিলাম,0,religion
হাসতে হাসতে চোখে পানি এসে গেছে 😂😂😂😁😁😆😅,0,religion
নাউযুবিললাহ,0,religion
এরা এ ধরণের জিকির থেকে বিরত থাকুক। এই কামনায় কেহ কেহ সংশোধন হচ্ছে এটার একটা ভিডিও করবেন। সাধারণ মানুষ তাদের খারাপ বলছেন তাই তারা ভূল বুঝতে পারছেন। ফিরে আসতেছেন আসল পথে। আপনাকে ধন্যবাদ এসব বাস্তব চিত্র তুলে ধরার জন্য। পরিবর্তন খুব প্রয়োজন যাচ্ছেতাই কাজ থেকে। আমরা আগের মত তাকওয়াবান আলেমদের চাই। যাদের ওয়াজে হেদায়েত হয় পথ হারা লোক। ধন্যবাদ।,0,religion
হুজুর রা পাদ দিলেও দুশ তাইনা। সালা ভাল হ,0,religion
হুজুর কথা গুলো সত্যি,0,religion
এই চার জনকে ফাঁসি দিতে হবে।না হলে শেখ হাসিনার মাথা এই জমিনে উরিয়ে ফেলা হবে।এই চার জন তো শেখ হাসিনার দালাল,0,religion
মুসলিম দেশ হয়ে ও আমরা এই নাফরমান কে হত্যা করতে পারিনা।আমদের ঈমান কি এতো দুর্বল?,0,religion
আমার একটি অনুরোধ রহিলো আপনাদের কাছে। বক্তা যখন ওলি আউলিয়াগনের ধারাবাহিক ভাবে বদনাম করতাছিলো ওনাকে বাধাদেয়ার পর। উনি তখনই ওলি আউলিয়ার ধারাবাহিক ভাবে সুনাম গাইতে শুরু করেছে এটার মানে কি?,0,religion
নাস্তিকরা মইরা নে তারপর দেখ কবরের আজাব কেমন লাগে,0,religion
মারফত কি বোজেন নি কমেন্ট সুদু বাজে করছেন তেহেরির পেসাবের সমান হতে পার বেন নি,0,religion
কুত্তার বাচ্চা কি বলে তা নিজেও জানে না,0,religion
🇧🇩আর বেশি দিন দূরে নয় যেদিন বাংলার যমিনে ইসলামী অনুশ্বাষন প্রতিষ্ঠিত হবে আলেমরা রাষ্ট্রীয় সম্মানে থাকবে এবং যেই সব ভন্ড রাম বাম নাস্তিক মুরতাদরা ইসলামকে নিয়ে ছিনিমিনি খেলছে তাদের বিচার সেদিন হবেই হবে ইনশাআল্লাহ।,0,religion
বন্ধুরা আমি তোমাদের জন্য নতুন একটি কোরআন তেলাওয়াতের চ্যানেল খুলেছি তোমরা সবাই আমার চ্যানেলটি ঘুরে এসে ভিজিট করো ভিজিট করে এসে ভালো লাগলো অবশ্যই সাবস্ক্রাইব করবে,0,religion
এসব নাস্তিকদের অনুষ্ঠানে যাওয়া টাই ঠিক না,0,religion
যে এই বিডিও বানাইছে ও আশলে একটা কাফেরের বাচ্ছা।,0,religion
সালাত প্রত্যেক মুসলমানদের জন্য ফরজ এবং ধর্মের অন্যতম ইবাদাত । সুফী সম্রাট হযরত শাহ্ দেওয়ানবাগী মাঃআঃ,0,religion
সালা বন্ড চিটিং,0,religion
মুক্তিযুদ্ধের চেতনায় যদি দেশ চলত তাহলে দেশ আরো উন্নত হতো এখানে কয়েকজন বলেছে মুক্তিযুদ্ধের চেতনায় দেশ চলছে আমি বলবো মুক্তিযুদ্ধের চেতনাকে জিন্দা কবর দেওয়া হয়েছে যেভাবে দেশ এখন খালি দেখি দেশে মারামারি কাটাকাটি খুনাখুনি মুক্তিযুদ্ধের আগে তো এরকম ছিল না তাহলে কি যুদ্ধের পরে আমাদের দেশে এরকম হল কেন,0,religion
মিজানুর রহমান আজহারি আমারব মুসলমানদের বন্দু,0,religion
বাইচা আছে কিভাবে,0,religion
তোমাকে দেখেই বেসি অবাক লাগে।বয়সের তুলনায় পাকনা বেসি। বিরক্তি কর ওয়াজ।,0,religion
আল্লাহ হুজুরকে হকের পক্ষের অটল থাকার তৌফিক দাও,0,religion
আপনাকে ধ্যনবাদ তাহেরী ভন্ড কিছু কথা ভিডিও দেখা তা হলে মানুষ এদের কাশ থেকে শোরে থাকবেন।,0,religion
দ‌েওয়ান বাগ‌ি তুই বড় ভন্ড,0,religion
আলহামদুলিল্লাহ আল্লাহ যেনো হুজুরকে নেক হায়াত দেন আমিন,0,religion
চারজন নাস্তিক কোরআন হাদীস সম্পর্কে কি বোজবে।,0,religion
আল্লাহ তাহেরি কে হেদায়েত দান করেন 😰😰,0,religion
তাকে যদি করে মেরে ফেলতে হবে,0,religion
আল্লাহ এই জাহেলকে হেদায়াত করুন আল্লাহ মামুলক সাহেবকে জাহেলদের থেকে হেফাজতে রাখেন,0,religion
এরকম সব ভন্ডদেরকে একটা লাইনে দাঁড় করিয়ে ব্রাশ ফায়ার করে মেরে ফেলে দেয়া দরকার!!!!!!,0,religion
ভাই! ওই সালায় ইলুমিনাটি 😡😡🤖😡,0,religion
কিরে নাস্তিক তরার কোনো কাছ নাই তরা ভাল হুজুরকে নিয়া আজেবাজে কথা বলি তরা তো নাস্তিক হে আল্লাহ আপনি হাফিজুর রহমান ছিদীক সাহেবকে হায়াত দিন আমিন,0,religion
এরে গালি দিলে গালির ও অপমান হবে😡🤬,0,religion
আসল ভনডো তাহেরী,0,religion
জুতা মার মু তর গালে,0,religion
এই নাস্তিক দের লজ্জা হয় না তোরা যদি নাস্তিক না হতি এখানে একটা কমেন্ট তো তোদের হয়ে কেউ করেনি তোরা কতো বড় মুর্খ নাস্তিক ভেবে দেখ একবার,0,religion
মানুষ বলতেই বুল উনাকে বুজালে তিনিতো বুজে জেতেন এভাবে গালি দেউয়া টিকান তুই একটি গরু তাই গালি দিছত,0,religion
এ লোকটা কে রে?,0,religion
এখানে হাফিজুর রহমান হুজুরকে আনা ঠিক হয়নি উনার ব্যপারে আরও জানুন,0,religion
মি জানুর খুব ভালো হুজুর তুমি থিক,0,religion
ভাল লাগল যে কেউ মুখ খুলল,0,religion
ভন্ডদের ছাড়া কেও পীর মুরিদি করেনা,0,religion
চুদ ব,0,religion
আল্লাহ তুমি আমাদের ঘরে ঘরে মিজানুর রহমান আজহারীর মতো নেক সন্তান দান করুন ।,0,religion
এতকিছুর পরেও কেন দেওয়ানভাগীর বিরুদ্ধে কোনো ব্যবস্থা নেয়া হয়না? রহস্যজনক বিষয়,0,religion
সবই বুঝলাম কিন্তু আপনি উনাকে দাজ্জাল বলে আখ্যায়িত করতে পারেন না।,0,religion
ওরে দেখলেই মেজাজ গরম হয়ে যায়। গীবত ছাড়া কিছু জানে না যারা ওরে দাওয়াত দেয় তারা বড় মূখ,0,religion
এতে জুতা মারা হুক সতান কে,0,religion
ওরা ভন্ডামীর সীমানা ছাড়িয়ে গেছে,0,religion
একাই একশ,0,religion
এমন বেয়াদবকে কারা দাওয়াত করে আওয়াজ করার জন্য,0,religion
নাস্তিকের বাচ্চারে জুতা মারো,0,religion
শয়তানের চেলা।,0,religion
হিজবুত তাওহীদ ভাই হিজবুত তাওহীদ কে করেন ওরা দেওয়ানবাগীর চেয়ে ও খারাপ,0,religion
আল্লাহ এই রকম নাস্তিক ছেলে মেয়েকে অবশ্যই কঠিন শাস্তি দিবে ইনশাল্লাহ,0,religion
আলহামদুলিল্লাহ হুজুর যেন এমনি ভন্ড পিরদের সমাজের শামনে আনতে পারে ওয়াজ মাধ্যমে,0,religion
এই চেনেল ইহুদিদের দালাল,0,religion
মদ খর সালা।,0,religion
এবার রোহিঙ্গা বলে গালি দিলেন গিয়াস উদ্দিন আত তাহেরী,0,religion
মিজানুর রহমান আহাজারী আমার খুব প্রিয় একটা মানুষ,0,religion
ভাই এই ভন্ড রে রোস্ট করে আপনি রমজানে বিশাল একটা পুণ্যের কাজ করেছেন।কিন্তু তারপরও কিছু আবাল চোদারা আপনার ভিডিওতে দেয়।যেসব আবাল রা দেওয়ানবাগীর ভক্ত আমার বিশ্বাস তাদের মধ্যে আবু জাহেল এর রক্ত বহমান।এইসব ভন্ডদের লাথ্থি মেরে বাংলার জমিন থেকে বিতারিত করতে হবে।,0,religion
খবরদার আলেম দের বিরুদ্ধে কেউ কথা বলবেন না,0,religion
ভন্ড দের আড্ডা,0,religion
ভন্ড আব্বাসী। ভন্ড তাহেরি আরো আছে।,0,religion
ভাই এসমস্ত ভন্ড বেদা আতি মাজার পূজারি এদের ভন্ডামি থেকে আমাদের কে সচেতন করার জন্য ধন্যবাদ,0,religion
এই শয়তান এই দেশে বাস করতে পারতেছে আমাদের বর্তমান সরকারের নাস্তিকপ্রীতির কারনে। গৃণা করি উভয়কে।,0,religion
তুমিতো বাবাজি জি বাংলা চ্যানেলের নাটকের শিশু শিল্পীদের মত অল্প বয়সেই ধান্দা শিক্ষা পালাইছো,0,religion
গরুটা একটু বেশী বলছে তবে অনেক হকও আছে,0,religion
যত্তগুলা আন লাইক দিছে সবগুলা ভন্ড দেওয়ানবাগীর ভক্ত!,0,religion
তুই তোর শয়তান দুনিয়াতে নাই,0,religion
? দাওনবাগী পইদা হন নাই ওনাকে টপকানো হইসে,0,religion
আলেম ওলামার ছোট খাটো ভুল না ধরে নিজের দিকে খেয়াল করেন। আপনি তো নামাজই পড়েন না মিয়া। তবে,0,religion
দুরু হালা ভনড,0,religion
উমরাহ হজ্জ করে চুল কামানো আর হজ্জ করে চুল কামানো কি জানতে চাই।,0,religion
মামুন ছাড়া সব নাস্তিক,0,religion
মহিলাদের মত । মাতায় কি দিছত শয়তান,0,religion
নবীজি বলছেন চুল একবারে ছোট রাখ না হয় বাবরি রাখ। আপনি প্রকার পাইলেন কোথায়।,0,religion
ওরে মারতে হবে এক হয় সবাই,0,religion
তিনি সব গুলো প্রশ্নের ভাল উত্তর দিয়েছেন। তিনি যদি না জানতেন জবাব দিতেন না। যদি তিনি ভুল বলেন। তাহলে ভুল ধরেন। না ধরে আপনারা বলেন যে তিনি না ও জানতে পারে। এটা আপনারা বেয়াদবি করেছেন। আশা করি বোঝতে পেরেছেন।,0,religion
ভাই রমযান মাস চলছে তাই তেমন কোন কমেন্ট করলাম না শুধু রোযা টা যাক আরো একটা কমেন্ট করমু 😠😠😠😠😡😡😡😡,0,religion
এই বমবলকে পাবনার পঠিয়ে দাও অখানকার পাগলেরা অর বেট দিয়ে ডোল বাজালে যদি ঠিক হয়।,0,religion
মাইজভান্ডারী মাইজভান্ডারী 😢,0,religion
ভায়া তুমি তুমার পাছাই আগুন লাগাও কিশের জন্য আজ বুঝতে পারছি😜😜😜,0,religion
ইতে মুনাপেক,0,religion
এইসব পীর দেখনা মরে দুইটা খাব না বারবার মনে কয় ???,0,religion
ভাই টিক,0,religion
এইসব নাস্তিক কে দিন দুপুরে প্রকাশ সে যবাই করে দেয়া উচিত,0,religion
শুিশু বক্তা কিয়ামতের আলামত আর কতো সুন্দর ওন্যর গিবাদ করছে শুধু মাইর দরকার,0,religion
তাহেরি কি তুকে কামর দিয়েছে,0,religion
জিহাদি হুজুরকে রোস্ট করার পর একটু খারাপ লেগেছিল এখন দেওয়ানবাগী কে রোস্ট করায় সেই কষ্ট টা ভুলে গেছি ভাই 😍😍😍,0,religion
নাস্তিকদের খুব জোরে জোরে জুতা মারা লাগবে,0,religion
আপু আপনি ঠিক বলেছেন।তাহেরী হুজুর নামে সনতারাস।বদমাইস আইনের আওতায় এনে সাসতি দেওয়া দরকার,0,religion
দেখেই বোঝা যায় যে কে ভন্ড কে আর আসল ইমাম,0,religion
বাংলাদেশ থেকে ভন্ড বাবা রপ্তানি করা হবে পৃথিবীর কোন কোন দেশ ভন্ড বাবা নিয়ে তাদের পাইকারি দরে ক্রয় করবেন আমাদের এই ওয়েব সাইটে ভিজিট করুন,0,religion
এখানে হয়তবা মানুষ কিছু দুনিয়াবি ফায়দা পাচ্ছে ও হয়তবা মনে করছে যে তাদের সকল কাজ দেওয়ান বাগিই করে দিচ্ছে আর তারা যে টাকা কামাচ্ছে মনে করছে যে এগুলো সব দেওয়ান বাগির বরকতেই হচ্ছে কাজেই উনাকে যদি এক লাখ টাকা দেই তাহলে দেওয়ান বাগি গায়েবি কারামতির দ্বারা তাকে দশ লক্ষ টাকার ব্যাবস্থা করে দিবে এগুলো হচ্ছে দেওয়ান বাগির ভক্তদের আকিদাহ্ আর মনে করে যে আল্লাহর যে ক্ষমতা দেওয়ান বাগির ও সেই ক্ষমতা আর দেওয়ান বাগির বিরুদ্ধে কিছু বল্লে কিংবা করলে মনে করে যে তাদের অনেক ক্ষতি হয়ে যাবে সে জন্যে তারা কিছু বলেনা আর দেওয়ান বাগির দরবারে ও খাবারের মধ্যে কুফরি করা কাজে ওখানে কোন ভালো লোক গেলেও এরকম উল্টাপাল্টা হওয়ার সম্ভাবনা আছে যা অতীতে এর অনেক প্রমাণ রয়েছে কাজেই উনাদের খাবার কোনোমতেই খাওয়া যাবে না ও দেখার জন্যে হলেও ওদের দরবারে যাওয়া যাবেনা এদের আস্তানায় আকস্মিক আক্রমণ করে সব তছনছ করে একেবারে ভেংগে নিশ্চিহ্ন করে দিতে হবে,0,religion
তোরে পাইলে জবাই করুম কাফের,0,religion
এই রকম ভিডিও আরো বানান,0,religion
এই আবালের দল কুর আন আর হাদিসের পার্থক্য জানেনা এরা নাকি বিশেষজ্ঞ,0,religion
কথা বলার সোজুগ দেয়না,0,religion
দেওয়ান বাগী কে নিয়ে রোস্ট করেছেন ভাল কথা কিন্তু আল্লাহর আকার আছে এইটা কুরানের আয়াত দ্বারা প্রমানিত আর হয়তো দেওয়ানবাগী ভুল কিন্তু তার কিছু কথা যেগুলা আপনি ভুল ধরেছেন কিন্তু সেগুলা মোটেও ভুল না,0,religion
ভিডিওটি দেখে হাসি থামাতে পারছি না।,0,religion
আল্লাহ আপনি তো সবই পারেন তবে এইসব মানুষকে ধ্বংস করেন না কেন,0,religion
ছাগল এখানে অপমানের কি আছে,0,religion
সালাম জানাই ছোট ভাই,0,religion
দেওয়ানবাগীর বিচি আমরা চাই ই চাই!,0,religion
তুরে জুতার বাড়ি দিয়া ইসলাম চারা করব শয়তান তুই তাবলিগ কে গালি দেস কেন আমার নামবার দেব তুই ফোন দিবি আমার কাছে তুকে আমার সামনে পেলে খুদারখচম তুরে দুনিয়া থেকে বিদায় করে দেব,0,religion
দুই হাতে ভকতা তিন আত নাই,0,religion
সব ভন্দামি,0,religion
শয়তান বলে কি,0,religion
ছি ছি প্রকাশে এমন ভাবে মুসলিম সমাজে নাস্তিক রা ঝামেলা করছে আর সবাই দেখছে ছি ছি,0,religion
এই সুলতানা কামালকে দেওয়া উচিত,0,religion
আমার একটা অনুরোধ এই সব শিশু বক্ত দের ওয়াজ না করানোটা অনেক ভাল,0,religion
গরুর পুটকি দিয়ে বাহির হয় গুবর। ওহাবীর পুটকি দিয়ে বাহির হয় ওহাবী। । এস এম ই রেজা,0,religion
হা হা😀😃অনেক হাশি লাম ভাই,0,religion
বালো কিচু দেখাইলে বালো লাগলো এরুকুম বিডিয় আরোচাই,0,religion
আব্বাসী তুই হইতো কাফেরর বড় ভাই তোর মধ্যে কোনো শিক্ষা নাই শিক্ষা নিলে তো শিখতি। তোর পতন খুব তারা তারি হবে ইনশাআল্লাহ 😠😠😠,0,religion
এক লক্ষ্য নাস্তিক ও যদি আসে আল্লামা মামুনুল হক এক আল্লাহর উপর ভরসা রেখে। একাই লড়াই করার সাহস রাখেন।,0,religion
নবিজিরসাতেকােনােকিছুরতুলনাচলেনা,0,religion
হুজুরের বন্ড মনগড়া কথা বলে মানুষকে গোমরা করতেছেন মিথ্যা কাজাব ।মাজারে নামেই ওল্ড ফুলডা বলিবেন না। জারা গনজা খাইতেছেন তারা জাহান্নামের দল,0,religion
এদের কে সোজা জবাই করে দেওয়া উচিত। একমত হলে লাইক দিন,0,religion
তর মত বেয়াদপ জেন বাংলায় আর জন্ম না নেয়। তুই বক্তা নামের কুলাংার।তর বাপের সমান মানুষ এখানে বইসা আছে তাদের সামনে আংুল লারাইয়া কথা কস,0,religion
শিশু বাচ্চা,0,religion
এসব ভন্ডদের দোষ দিয়ে লাভ কি এদের যত ভক্ত আছে তাদের কে জুতাপিটা করে বাংলা দেশ থেকে বের করে দেওয়া উচিত,0,religion
ওরা নাস্তিক,0,religion
একটা জুতা মারতে মন চায় ওরে,0,religion
এই নাস্তিক দের কেউ জেনো যানাজা না পড়ায় এটা আমার অনুরোধ,0,religion
দেওয়ান বাগীর কপালে জুতা,0,religion
ইনশাআল্লাহ সামনে জবাই করবো হুদার কসম নাস্তিক মুরগি কবির তরে জবাই করবো,0,religion
এটা একটা বাছাইকৃত বেয়াদব,0,religion
ভাই আপনাকে ধন্যবাদ,0,religion
নেক্সট ব্রেন্ডন ম্যাককালাম,0,religion
তোদের উপর আল্লাহর গজব পরুক,0,religion
তারকাটা,0,religion
সামনা সামনি যদি পাই তোরে মুরগী কবির তোকে মুরগি বানিয়েই ছাড়ব।,0,religion
আসসালামু আলাইকুম ভাইয়া ভাইয়া আপনার কথাগুলো অনেক ভালো লাগছে চেষ্টা করবেন আরো আগে যাওয়ার জন্য আমরাও দোয়া করব আরো আগাই যান কিন্তু সবকিছু বুঝে শুনে করবেন,0,religion
ভিডিও তে অনেক ইনফরমেশন অন্য ভিডিও থেকে কপি করা,0,religion
আমাদের নারায়ণগঞ্জ আসস না কেনো তাহলে জোতা দিয়া পিটাইতাম,0,religion
এই অবস্থায় যদি এইসব ভন্ড যদি হাজারো ভুল করে কিন্তু সরকার তা দেখবে না কারণ সরকার তাদের গোলাম। আমরা সাধারন পাবলিক যারা বুঝি তাদের বিরুদ্ধে যদি কোন প্রতিবাদ করি তাহলে সরকার আমাদেরকে উল্টা আইনগত ব্যবস্থা নেবে,0,religion
সয়তান কাজজাব আললাহর কামতন্ত্র,0,religion
তিনটি নাস্তিক আর এক জন আলেম।।,0,religion
তোরে ভালো জুতা দিয়া মারলেও জুতা সরম পইবো ছেড়া জুতা দিয়া মারতো হইবো।,0,religion
ওরা যেমন আমাদের চমক দেখাইছে আমরা তেমন চমক দেখতে যাচ্ছি আর তা হল তাদের জনের কুত্তার মত মৃত্যু কাররণ মিলিয়নের মধ্য মিলিয়ন ঈশ্বর এ বিশ্বসি এরা যাইব কোই এখানেই তো এরা মরবে কমনে মরছে তার উপর একটা ভিডিও বানইও ভাই,0,religion
আল্লাহ পাক তোদের হেফাজত করুণ না হয় ধংস করে দিন আমিন,0,religion
না বুইঝা লাফালাফি কইরা ভিডিও বানাছ কেন??? মানুষরে ভুল তথ্য দিয়া ভুল পথে কেন নিতেছিস?? তোরে কি কেউ টাকা দেয় এটা করার জন্য??? আজহারি হুজুর এর কথা বলছে সে এই কথা দিয়ে কি বুজিয়েছে?? তাতো জানোস নাহ ভুল ভাল তথ্য দিয়া সাধারন মানুষকে বিপদে ফালাইতাছিস। এই নিয়া কত ভিডিও হয়ছে তুই খুজে দেখ ইউটুবে আশাকরি বুঝতে পারবি যে আজহারি হুজুর,0,religion
কাফেরদের সাথে কথা বলে নিজেকে ছোট করার দরকার নেই।,0,religion
আপনাদের মত কিছু পাগল ছাগল ইউটিউবারদের কারণেই তাহেরিরা জন্ম নেয়। যেদিন আপনাদের মত পাগল ছাগল ইউটিউবার থাকবে না সেদিন তাহেরিরাও থাকবে না,0,religion
তাহেরী একটা বেয়াদব ওকে যা বলা যায় তাই বলছে,0,religion
তোরে কাছে পাইলে একটা জুতার বাড়ি হলে ও দিব,0,religion
হুজুরের আজান শুনে কলিজা ঠান্ডা হয়ে গেলো।,0,religion
এই কথা গুলো ইন্ডিয়ায় যেয়ে বলে দেখ তো ওরা কতটা অসাম্প্রদায়িক???,0,religion
শুভ কামনা রইল হুজুরের জন্য,0,religion
আমি আলেমদেরকে কিছু কনক আলমদের গেছে বলছেন আপনি নিজে একটা দালাল,0,religion
এদের জুতা মারা দরকার,0,religion
এ আব্বাসি কে শয়তান পরিচালনা করে তার ওয়াজ শুনে আমল করলে শয়তানকে অনুসরণ করা হল,0,religion
এসব টিভি চ্যাঁননেলও সাংবাদিকদের পুড়ে দেয়া হউক।,0,religion
আমির হামজা দুকাবাজ সে প্রথমে বলছে এক কথা এখন বলতেছে আরেক কতা,0,religion
হে আল্লাহ নাস্তিকদের কে হেদায়েত দান করুন এরা হয় তো অনেকেই কাফের ইহুদি নচরাদের দালাল টাকার কাছে বিক্রি হয়েছে আল্লাহ এদের কে সঠিক জ্ঞান দান করুন আমিন !,0,religion
ভন্ডামি তাহেরি,0,religion
লাথি দিয়ে খেদানো দরকার,0,religion
মিজানুর রহমান আজহারী ভাই নিয়ে করা ঠিক না,0,religion
বিশ্ব ভেরিফাইড নাস্তিক আসিফ মহিউদ্দিন নিয়ে ভিডিও করুন। প্লিজ প্লিজ প্লিজ প্লিজ প্লিজ প্লিজ প্লিজ প্লিজ প্লিজ।,0,religion
আল্লাহ পাক এদের উপর গজব নাজিল করুন,0,religion
ভন্ড পীর । তুমি বল পায়খানার ডুকার সময় দোয়া করতে হয় তাহলে তখন হাত দুলতে হবে?,0,religion
বন্ডদের যিকির আল্লাহ্ আল্লাহ্!!! আশ্চর্য কথা!!! তাহলে যারা মূর্তির যিকির করে তারাই হক??,0,religion
এ বেয়াদপ তোকে মাহাফিল আনছে কে,0,religion
মাইয়াতো জাজেস হয়ে গেলে😂,0,religion
ভাই এদের কোন দোষ নাই সব দোষ হলো তাদের বক্তদের কারন তারা কেনো জায় এমন ভন্ডপীর দের কাছে,0,religion
জিনা সে বন্ডনা তাহেরি সত্য কথা বলে,0,religion
আমার বাড়ি সিলেট আমি অনেকবার দেখেছি শাহজালাল মাজারের পিছনে নষ্টা নারিদেরকে নিয়ে গাজা টানে।,0,religion
পুরান ঢাকায় আগুন লেগে কতো ভাল ভাল মানুষের মৃত্যু হয়েছে এই ভন্ড মাজার পূজারি দের ধ্বংস করলো না কেন আল্লাহ পাক এদের কি চোখ দেখেনা,0,religion
এদেরকে ফাঁসি দেয়া হোক,0,religion
নাস্তিক টা।,0,religion
তাহেরীর বাপ হবে এটা এই বয়েসে এতো পাকছে ওয়াজ বাদ দিয়ে ভাশন ছাড়তাছে এই বয়েসে এটা মানায় না,0,religion
নাউজুবিল্লাহ আমি এতকিছু বুঝিনা কিন্তু এটা বুঝি দেওয়ানবাগী শালা তুই একটা কাফের মুসলমানের দেশে কি মানুষ বাঁচে রাখছে কিজন্যে আমি বুঝিনা হে আল্লাহ আমাকে সেই শক্তি দিন ইসলামের শত্রুকে ধ্বংস করার জন্য,0,religion
শয়তানতুই তেহেরী,0,religion
লোপা রহমান তুই মরে দেখ আল্লাহ তোর জন্য জাহান্নাম রেডি করে রেখেছে,0,religion
এই জন ইসলাম বিরুদি।নাস্তিক আর একজন মুসলিম।,0,religion
কাজী ইব্রাহিম বহুত বড় বন্ড,0,religion
নিজেরে নিজে হুজুর বলে,0,religion
তুমি তো নামবার ওয়ান বেয়াদব কারন,0,religion
ভাই আপনার মাথায় টুপি থাকলে আরো ভালো লাগতো।,0,religion
শেখ হাসিনা রাজাকার ধরতে পারে কিনু নাস্তিক ধরতে পারে না।কি বলব ওই তো নাস্তিক।।।।।।।।,0,religion
বদমাশ তাহেরি,0,religion
তোমার ক্যাপ দেখে মনে হচ্ছে তুমি খ্রীষ্টান🤒🤒,0,religion
তাহেরি যে ভনড তা ওর গেট আপ দেখে বুঝা যায়,0,religion
এতো খারাপ ভিডিও আবার সেয়ার করতে বলছেন আপনি ও এদের মধ্যে একজন ফালতু।,0,religion
এরা আলেমদের ছোট করার চেষ্টা করছে এরা হুজুরকে তো কথা বলতে দিচ্ছেই না।,0,religion
বেয়াদব ছেলে তোর গালে জুতা মারা উচিত,0,religion
মুফতি মাসুদ এটা কি করলো? কলিজায় তীর মারলো!,0,religion
ভায়েরা আপনাদের অনেক ধন্যোবাদ এগিয়ে জাও তোমার পাসে আছি ভাই ?,0,religion
এই নাস্তিকের দিমাগে আল্লাহ তা আলা চাবি মেরে রেখেছেন।জার কারনে হুজুরের কথা গুলো তাদের কানে পৌছায় না।আমি দোয়া করি আল্লাহ তাদের কে হেদায়েত দান করুন ।,0,religion
কিসের সাথে কিসের তুলনা!,0,religion
হুজুর কেন নাস্তিকদের সাথে তর্ক করতে গেলো বুঝলাম না,0,religion
নাস্তিক তোদের ফাসি চাই,0,religion
আসলে ভাই কি বলবো ওদেরকে ধরে কি করা উচিত জানেন বাংলাদেশ অতিরিক্ত ডেঙ্গু মশা হয়ে গেছে ওদেরকে ধরে ডেঙ্গু মশার কাছে দিয়ে দেওয়া উচিত তাহলে সাধারন মানুষ বেঁচে যাবে,0,religion
বেয়াদব তাহারি ওয়াজ না করে গান গা কত বড় বেয়াদব,0,religion
তাহেরি হুজুর তকে কি করছে,0,religion
মাওলানা মামুনুল হক সাহেব এই খানে আসা ঠিক হয়নি। কারন হল এই নাস্তিক গুলি সরকারের খুটির জোরে কি থেকে কি বলে না বলে কোনো খেয়াল নেই।,0,religion
সাবাস বাঘের বাচ্চারা,0,religion
আল্লাহ এদের কে সঠিক পথে চলার তৌফিক দান করুন আমীন সুম্মা আমীন,0,religion
মিজানুর রহমান অাজারি 😍😍 ভালোবাসা অবিরাম,0,religion
এরা সব মাজার পূজারী ভন্ডের দল জিকির নামে ধর্মের ব্যবসা চালাচ্ছে শয়তানের দল ইবলিশ শয়তানের দল মিজানুর রহমান আজহারী অনেক অনেক অনেক শান্ত বক্তা আল্লাহতালা উনাকে হায়াত দান করুন আমীন আমীন আমীন,0,religion
ভালোবাসার একজন মানুষ মিজান ভাই♥♥♥,0,religion
কি বলবো এদের সমন্ধে এরা এতোটাই যঘন্ন যে এদে মুখ দেখও গোনা হবে। নাউযুবিল্লা,0,religion
ধন্যবাদ প্রিয়ভাই অনেক কিছু শিখতে পারছি। কিন্তু ভাই আমরা অন্যায়ের বিরুদ্বে রুখে দাড়াতে পারছিনা কেন ? ভাই আপনি এগিয়ে যান। দোয়া করি আপনার জন্য 😍😍,0,religion
ওর তো মুখ দিয়ে কথাই আশেই না কী ওয়াজ করবে।,0,religion
ও তাহেরি কে বলার কে। ওর বয়স হইছে। তাহেরি যেমন এই হোক ও বলার কে বেয়াদব।।বেয়াদব বেয়াদব,0,religion
তুই আবার হুজুর হইলি কবে,0,religion
আমির হামজা সাহেবের কাছে আমার একটা প্রশ্ন ছিলো।।তিনি কি দেওয়ান বাগির বিরোদ্ধে কোনো পদক্ষেপ নিবেন কিনা।।।,0,religion
শালাদের বোমা মেরে উড়ে দেওয়া হউক 😰,0,religion
আসসালামু আলাইকুম কেমন আছেন সিলেট হবিগঞ্জ থেকে বলছি ভাইয়া গান বাজনা এবং ছবি করা জাই কি না জানাবেন প্লিজ ধন্যবাদ আরিফা,0,religion
ওরে প্রকাশ্যে উলঙ্গ করে পাথর নিক্ষেপ করে জাহান্নামে পাঠানো উচিৎ। সে প্রকৃত পীর নয় সে ভন্ড পীর।,0,religion
দেওয়ানবাগী রে যদি পাইতাম আগে রড গরম করতাম একদম লাল করে তারপর পাছায় ঠান্ডা মাথাটা ঢুকাই দিতাম আর গরম মাথাটা বাহিরে রাখতাম যাতে এটা কেউ বের করতে না পারে।,0,religion
আমি আগে আপনার ওয়াজের বক্ত চিলাম এখন জানতে পারলাম আপনি এক জন বন্ড ।আপনার কাছে ইসলামে কনো গেয়ান নাই।,0,religion
ড জাকির নায়িক থাকলে বুজতে নাস্তিকের দল,0,religion
এই বক্তা যে আল্লাহর অলির দুশমন তাতে কোন সন্দেহ নাই এ ভয়ে আল্লাহর অলির কিছু প্রশংসা করলেও এরা আল্লাহর অলি মানে না এ বক্তা কে জুতা মারা দরকার ছিল এটা শয়তানের দল যে প্রতিবাদ করেছে সে প্রকৃত ঈমানদার আল্লাহর রাসূল প্রেমিক অলি প্রেমিক আল্লাহ প্রেমিক,0,religion
আমি এই চার নাস্তিক কে জুতাপেটা করতে চাই আপনারা কি চান,0,religion
ভাই সবাইকে ভণ্ড বল্বেন্নে যাচাই বাচাই করুন তার পর বলুন আপনি যান দেয়ানবাগে যান আত্রশি যান সুরেশ্বর যান চন্দ্রপুরি আগুলুও দেখুন আর চরমনাই উজানি সারসিনা আগুলো ও যাচাই করুন দেখেন কারা ভণ্ড আর কারা আসল,0,religion
ওর বয়স কতো পাগল দলের পাগল তার জ্ঞান কতটুকু সে কোরআন থেকে কি বিশ্লেষণ করতে পারবে হাই কি দুনিয়া আচ্ছা এর কাছে একটা প্রশ্ন কার কথা কপি করে কি বলবো ভাষা নেই যদি তুরাই সত্যি বলে দাবি করিস তাহলে তুরা যেখানে যাস সেখানে বাশ খাস কেনো তুই পিচ্চিটা বলে হুজুর মুখ দুধের গন্ধ যায় নাই তুই বলিস কে আলেম কে না ওয়াবি হলো একটা বেদে জাতি যার কোনো কুল কিনার নেই আচ্ছা তুরা যদি এত বড়ই হস তুদের সেই বড় বড় শাইখুল হাদিস রা কই যারা কোনো চ্যালন্জ এ আসে না তারা বসে বসে দুধু খায় কি বলবো তুদের হুজুর নিজেই বলে ছোট বক্তা খিয়ামতের আলামত 😃তুদের মুখে এক কথা পুন্দে এক কথা তুদের সম্পর্কে বললে পাপ হবে পাবনায় থেকে নাকি কিছু পাগল কিছু বছর আগে পালিয়েছে ওরা নাকি এরাই বড় আলেম😃😃,0,religion
লাভ ইউ ভাই 😍,0,religion
ভন্ঢো তো ভন্ঢো,0,religion
বন্ডদের আড্ডা খানা,0,religion
স্বামী স্ত্রীর বন্ধন দৃঢ় করতে স্ত্রীর টি হক পূরণ করুন!   স্বামীর সন্তুষ্টিতে স্ত্রী জান্নাতি   পরকীয়ার পূর্বেই পরিণাম কত ভয়াবহ অবশ্যই জেনে নিন   জীবন সাথী নির্বাচনে ইসলাম কি শর্ত দিয়েছে জেনে নিন।   স্ত্রীর যে টি গুন সংসার সুখময় ও স্থায়ী করে।   সফল দাম্পত্যজীবনের বাস্তব উদাহরণ   সফল দাম্পত্যজীবনের বাস্তব উদাহরণ   বিবাহিত জীবন সুখী করতে টি উদ্দেশ্য বাস্তবায়ন করুন!,0,religion
ভাই এগুলাহলো বন্ড়ামি,0,religion
ভাই আপনি যাদের কথা এখানে উল্ল্যেখ করেছেনতার মধ্যে দুই জন ভালো মানুষকে ভন্ডদের সাথে মিলিয়ে ফেলেছেন হাফিজুর রহমান চরমোনাই এর হুজুরআমি মনে করি বাংলাদেশে যত হক পন্থি আছে তার মধ্যে চরমোনাই অন্যতমবিশ্বাস না হলে আপনি নিজেই যাচাই করে দেখুন,0,religion
এই হালা কোনটা আবার মার দেন,0,religion
এরা ধর্মের নামে ব্যবসা করে এদের কে জুতা পিটা করা দরকার এদের বিপক্ষে সরকার তো কিছু বলে না তাই আমাদেরই করা দরকার জুতা পিটা,0,religion
ভাই অপনাকে ধন্যবাদ,0,religion
দেওয়ানবাগী তো পীর নয় সে একটা ভন্ড যদি তােরে স্বপ্নে ও পাইতাম তারে আমি ওইখানে জুতা দিয়া পিটাইতাম যত মাজারিরা আছে সব সবগুলার মাথায় ডিস্টার্ব আছে মাজারে কি ভাল মানুষ থাকে তাছাড়া রাসূল সাল্লাল্লাহু আলাইহি ওয়া সাল্লাম মাজার এর বিপক্ষে ছিলেন তিনি বলেছেন যারা মাজারের খাদেমরা নিকৃষ্ট,0,religion
এই বিডিও যে বানাইছে সে কোন ধরনের মুসলিম বুজলামনা,0,religion
ও শালার পুত তর নাম্বার দে,0,religion
শালা ভন্ড গিয়াস উউদ্দি তাহেরী 😀😀😀😀😀 খাজা বাবা গোলাপশা বাবা😀😀,0,religion
এই মাল টার পেছনে বাশ আছে,0,religion
ভাতিজা আওয়াজ এতো বড়ো কেন,0,religion
ঠিক বলছে মুরুব্বি,0,religion
মিজানুর রহমান আজহারী আমাদের প্রিয় বক্তা অকে যে বন্ড বলবে ওই নিজেই বন্ড,0,religion
আল্লাহ হেদায়েত দান করুন,0,religion
মুরখোর বাচচারা তোদের জন্যে আমাদের একটা ভাই ই যথেসট,0,religion
যিকির না পাগলের নাচ,0,religion
এই জালেম দেরকে জিবিত পুরিয়ে মারার দরকার,0,religion
এগুলা আগেই দেখছি তবুও বলছি এদের দেওয়ানবাগীর পার্থক্য কি? জানতে পারলে খুশি হইতাম।,0,religion
কারা জায় এই ভন্ডদের কাছে😣😣😣,0,religion
আপনিত এখন তাহেরীর কাছে মাপ চাইতে হবে?,0,religion
জত ভন্ড আছে সব ভন্ড কে একটা ভন্ড ছারপাবেনা,0,religion
আমি সবসময় মানুষের মুখে শুনেছি এই ভন্ডের কথা কখনো উনার ভিডিও দেখিনি কারণ অনেক খারাপ লাগে যখন আমার আল্লাহ ও নবী রাসূলদের নামে এই রকম নোংরা কথা গুলো বলে আমি জানি না আমি কতটুকু সাত্তিকারের মুসলিমের দায়িত্ত্ব পালন করছি তবু ও অনেক কষ্ট হয় এইসব ভিডিও দেখতে। আজকে দেখলাম আল্লাহর সৃষ্টির সেরা জীবই নাকি আল্লাহর নামে এইসব কথা বলে। শুধু এতটুকুই বলতে চাই আল্লাহতালা তার সকল মুমিন মুসলিম বান্দা দেড় সঠিক পথে চলার তৌফিফ দান করুক আমীন,0,religion
মাথা পুরো গরম হয়ে গেল আল্লাহ বাংলাদেশে ইসলাম রক্ষা কর!!!!!,0,religion
নাস্তিকের বাচচারা এগুলো করে,0,religion
এই জন হক বক্তা মৌলানা সাহাব,0,religion
নবির বিরুদ্ধে বললে এই পির পুজারিদের কিছু আসে যাই না। কিন্তু ভন্ড পির দের বিরুদ্ধে বললেই ঝামেলা শুরু করে শয়তানের খালু।।।😠😠,0,religion
ওদের মতো বক্তারা ইসলাম ধর্মের আবর্জনা,0,religion
আশরাফুল মাদারিস শায়খুল ইসলাম জামে মসজিদ খানকাহ শায়খ আখতার রহ হজরত মাওলানা শায়খ নাসির উদ্দীন মাহমুদ শাহ সাহেব আশরাফাবাদ আশরাফাবাদ আশরাফাবাদ,0,religion
মা ফাতামা বলে আবার বউ বলে,0,religion
হালায় ভন্ডা বক্তা,0,religion
আমার কাছে হুজুরকে অনেক ভাল লাগছে কারণ হুজুর হকের পক্ষে কথা বলেছেন। আবার ঐই লোকটিকে সুন্দর করে বোঝিয়ে দিয়েছেন। আল্লাহ আমাদের সকলকে সহি বোঝার তৌফিক দান করোন আমিন।,0,religion
আল্লাহু আমাদের কবুক ও মঞ্জুল করুন,0,religion
ওদের বিচার হয়না কেনো জানেন কারন আমরাই বালো না,0,religion
মিজানুর আজাহারী ভুল করেছি,0,religion
ভন্ড তাহিরী আরো অনেকে কিন্তু মিজানুর রহমান একজন ভালো বক্তা ভালো মানুষ,0,religion
বাংলাদে জদি ভালো হুজুর থাকে তাহলে মিজানুর আজহানি আমার মতে,0,religion
চারজনের সঙ্গে একজন পেরে ওঠা মুস্কিল। কমেন্ট দেখে অনুমেয় নাস্তিক অথবা হুজুর বাদে চারজনের মতের পথের অনুসারীর পরিমান। আফসোস ওদের বিয়ের সময়ও একজন হুজুর লাগে মৃত্যুর সময়ও লাগে একজন জানাজা সালাত সমাধায়।,0,religion
ধন্যবাদ দেওয়ানবাগীর ভন্ডামী দেরীতে হলেও তোলে ধরে তুলুধুনা করার জন্য। পাডা পুতায় গ্রামের মহিলারা মশলা পিশায় কিন্তু এরা মশলা না পিশিয়ে মেয়াদ উত্তীর্ণ গাজা সাথে আনুষাঙ্গিক পিশায় আর ভক্ষণ করে।,0,religion
সামার পো,0,religion
ভাই এই রকম ভিডিও আর করবেন না,0,religion
টিক বলেস ভাই তোফাজ জল একটা হাই,0,religion
নতুন পাগলের আমদানি হোইছে,0,religion
এডমিন তুই কি মনে করছোস এইসব মিথ্যা গুজব ছড়িয়ে মোহাম্মদী ইসলামের আলো নিভিয়ে দিবি কারণ আল্লাহ নিজেই কোরআনে বলেন নিঃচই আমার বন্ধুদের কোন ভয় নাই তারা কোন কারণে চিন্তিত হবে না।,0,religion
ওদের পাগলামি দেখে শয়তান অবাক,0,religion
মুরগি চোরকে জুতা মারা উচিত।,0,religion
ভাই ও বোনেরা আপনারা এত হতাশ হবেন না আল্লাহ আমাদের মত তারাহুরো করে বিচার করেন না উনি অনেক ধয্য শীল শুধু দোয়া করুন এই নাস্তিকদের বিচার যেন হাসরের ময়দানে আল্লাহহপাক আমাদেরকে একবার দেখায় আমিন,0,religion
আমরা বলি তাহেরি একটা বন্ড তাহেরী বলে আমরা ভন্ড আললাহ ভালো জানেন,0,religion
ভাইর কন্ঠে কলিজা ঠান্ডা হয়ে গেল।,0,religion
হে আল্লাহ এই ইহুদির হাত তেকে আল্লামা মামুনুল হক কে সহজ করে দেন,0,religion
আপানর ভিডিওটি আমার ভালো লাাগছে। মিজানুর রহমান আহজারি বাংলাদেশর গৌরব আমাদের অহংকার।,0,religion
সালাফীজাম নিয়ে আব্বাসী সাহেব সর্ম্পকে একি বললেন তার পি এস মাও মুফতি আহমাদ হাসান গাজীপুরী সালাফীজাম নিয়ে আব্বাসী সাহেব সর্ম্পকে একি বললেন তার পি এস মাও আহমাদ হাসান গাজীপুরী সালাফীজাম নিয়ে আব্,0,religion
বাংলার মুসলিমদের কলিজা হল মিজানুর রহমান আজহারি।,0,religion
ইসলামকে ধংস করার জন্য তাকে আগুনে জলসে দেওয়া উচিত।,0,religion
ভালো কে ভালো বলবা খারাফ কে বলবা,0,religion
মিজানুর রহমান আজহারী সটিক।৷৷৷৷৷ ভন্ড তাহেরী মাজার পুজারী কাফের।,0,religion
সত্যি কথা সয়তানের গায় আগুন জ্বলে।আল্লাহ রহম করুন।,0,religion
প্রায় প্রত্যেকটা হুজুরের ওয়াজ শুনেছি এই লিস্টের। আপনি সত্যি বলেছেন ভাই। ওনাদের আকিদায় অনেক সমস্যা আছে। ইসলামিক মাদ্রাসাতে পড়েও ওনারা ইসলাম সম্পর্কে কিছুই শিখতে পারে নাই মাঝেমধ্যে তাই মনে হয়। শুধুমাত্র পাশ করার জন্যই মনে হয় পড়াশোনা করেছে। বাস্তব জীবনে ইসলাম প্রয়োগ ও অন্যকে শিক্ষা দেওয়ার জন্য শিখে নাই। সহিহ হাদিস থাকার পরেও ওনারা সব বাদ দিয়ে বুজুর্গদের বয়ান করেন। বুজুর্গরা কি আমল করেছেন তা আলোচনা করেন। অথচ নবী সাল্লাল্লাহু আলাইহি ওয়াসাল্লাম কিভাবে আমাদের শিখিয়ে দিয়ে গেছেন সাহাবায়ে কেরামরা কিভাবে আমল করেছেন এসব নিয়ে কোন আলোচনা করেন না। খালি বুজুর্গ আর পীরের বয়ান। নবী সাল্লাল্লাহু আলাইহি ওয়াসাল্লাম বলেছেন আমার উম্মতের মধ্যে সর্বশ্রেষ্ঠ উম্মত হচ্ছে আবু বকর রাঃ । কই কোনদিন তো শুনলাম না যে উনি কেরামতি করে এই করেছেন সেই করেছেন। খালি নাকি আল্লাহ পাক বুজুর্গদেরই সুপার পাওয়ার দিয়েছেন। আথচ সর্বশেষ্ঠ উম্মতের কোন কেরামত নাই। ভাইয়েরা আমার মনে রাখবেন ইসলাম কারো বাপ দাদার সম্পদ না। এটা আল্লাহ পাকের পক্ষ থেকে আমাদের জন্য একটা রহমত। এটাকে ঠিক তেমন ভাবেই বুজতে হবে যেমন করে আমাদের প্রাণের নবী সাল্লাল্লাহু আলাইহি ওয়াসাল্লাম বুঝিয়ে দিয়ে গেছেন এবং সাহাবায়ে কেরামরা যেভাবে আমল করে গেছেন। তার থেকে বেশিও করা যাবে না আবার কমও করা যাবেনা। মনে রাখবেন ভাইয়েরা প্রত্যেক ধর্মেই এমন কিছু যাযক পুরহিত হুজুর থাকবে যারা কিনা ধর্মের নামে ব্যবসা করে। মিথ্যা কথা বলে মানুষের মন নিয়ে খেলে ও সত্যি ধর্ম থেকে মানুষকে অনেক দূরে নিয়ে যায়। আর আমরা সাধারণ মানুষ চিন্তা করি যে ওনারা তো অনেক জ্ঞানী মানুষ মিথ্যা কেন বলবে? ইতিহাস দেখলেই বুঝা যায় ভাই এই ধর্ম ব্যবসা যে কি রমরমা। ভাইয়েরা আমার ইসলামকে নিয়ে পড়াশোনা করুন। ইসলামকে মনে প্রাণে ভালোবাসুন। সহিহ দলিলের অভাব নাই বিদাত ও শির্ক বাদ দিয়ে চলুন না আজ থেকেই সহিহ আমলের চেষ্টা করি। আমরা আমাদের প্রচলিত সমাজ থেকে ইসলাম সম্পর্কে যা জানতে ও শিখতে পেরেছি চলুন না কোরান ও হাদিসের বই গুলো খুলে যাচাই করে নিই আমাদের আমাল গুলো সাহাবায়ে কেরামদের মতো হচ্ছে কিনা নবী সাল্লাল্লাহু আলাইহি ওয়াসাল্লামের শিখানো পথে আছে কিনা চলুন না যাচাই করে নিই। ভাইয়েরা আমার ইসলামকে আবেক দিয়ে বুঝলে চলবেনা ইসলামকে বুঝতে বিবেক লাগবে। মনে রাখবেন ভাইয়েরা আমাদের সমাজ এখন অসংখ্য মুনাফেক দিয়ে ভর্তি। কোন হুজুরের কথা কোরান হাদিসের রেফারেন্স ছাড়া বিশ্বাস করবেন না। জীবনকে কোরান ও সহিহ হাদিস দিয়ে গড়ে তুলি সবাই। ভন্ড হুজুর পীর শির্ক বিদাত থেকে নিজেদের সবাই বাচিয়ে চলি। আল্লাহ পাক আমাদের তৌফিক দান করুক। আমিন। আসসালামু আলাইকুম।,0,religion
লোপা তোরে পাইলে তোরে দিয়েই জিহাদটা শুরু করতাম,0,religion
গেদগু গেদগু,0,religion
নাস্তিকদের সাথে কেন বৈঠক করতে গেলেন এই আলেম। সব শয়তান।,0,religion
আসসালামু আলাইকুম আমির হামজা ভাই আপনি ঠিক কথাই বলেছেন একজন আল্লাহর বান্দা কখনো এভাবে জিকির করতে পারেনা তাহের হোসেনের ফাঁসি চাই,0,religion
ভাই অনেক ধন্যবাদ,0,religion
আরে বাটপার তো তুমি মিয়া। একজন শিশু মানুষ হয়ে তুমি একজন বয়স্ক লোকের বিরুদ্ধে এরকম কথা কইতাছো। তারে কিছু বললে বলতে পারো তোমার বাবা অথবা তার সমবয়সী যারা আছে তারা। তুমি তারে জ্ঞান দেওয়ার কে। চুনোপুটি। মেনে নিলাম সে অপরাধী তুমি তো বলার জ্ঞান রাখ না তারে। বোকার মত বেয়াদবের মত কথা বল মিয়া। তুমি যদি আলেম হও তোমার সোফার পাশে তোমার বয়সে বড় একজন ব্যক্তিকে কেন বসাইছো নিচে। তুমি আবার অন্য রে জ্ঞান দাও তাইনা। আগে নিজে ভালো মত শিক্ষা গ্রহণ করো। পরে তোমার সমবয়সী অথবা ছোটদের জ্ঞান দিবা। মনে করতে পারো আমি তাহেরির পক্ষের কোনো লোক। তাহলে সেটাও তোমার ভুল হবে। আমি একজন মুসলমান। আর তোমরা মুষ্টিমেয় কিছু বক্তা যা শুরু করছো। এতে মুসলমানরা বিধর্মীদের হাতে বিভ্রান্তিতে পড়ে গেছে। একজন আরেকজনরে গালাগালি শুরু করছে আর একজন আরেকজনকে গালি দেয় এগুলা কি। সব জালিয়াতের দল।,0,religion
যে অন্য লোকের গিবত গায় সে কোনো দিন ভালো হতে পারে না,0,religion
মাজারে গাজাখায়েএটা সত্তকথা,0,religion
এই খানে কিছু ভন্ড ও মাজার পূজারী এসেছে।,0,religion
তর ফকিরবিৰুদেজানা নাই ভনডদেৰ পাও দৰে থাক,0,religion
মুসলমানের দেশে মাজার পুজারী ভন্ড থাকবে না ইনশাআল্লাহ!,0,religion
এইটা ইসলামি সংগীত,0,religion
সব ভণামি,0,religion
এই মানুষটা কে জুতো মারা দরকার ।বিয়াদব মাওলানা সাতে বিয়াদবী করে।,0,religion
আব্বাসী সঠিক,0,religion
এই চ্যানালের মালিক তোমালে বলছি হাফিজুর রহমান কতা বলার আগে চিন্তা কর।,0,religion
ভাই যারা পীরের মুরিদ হয় তাদের কিছু বুঝানো যায় না তারা সব সময় বেশি বুঝে।,0,religion
এই নাস্তিক গুলোই এখনো বেঁচে আছে কেমনে মুসলমান থাকতে এদের ফাঁসি হয় না কেন এখনো,0,religion
সব নাস্তিকদেরকে জুতার বাড়ি দিয়ে বাংলাদেশ থেকে বের করে দেওয়া উচিত,0,religion
ফাজিল শব্দের অর্থ তো সম্মানিত ফাজিলের ওপর উচ্চ ডিগ্রী লাভ করতে গেলে সম্মানের উপর উচ্চ ডিগ্রি লাভ করতে হবে তাহলে কি আপনি বলতে চাচ্ছেন এই দেওয়ানবাগী সম্মানের ওপর উচ্চ ডিগ্রি লাভ করেছে???,0,religion
কোন সালারা জে ডিছলাইক দিছে কে জানে আমি প্রাথনা করি জে আল্লাহ জেনো জাহান্নামে তাদেরকে নিক্ষেপ করে আমিন,0,religion
এসব সালাদের কনো বিচার নাই এদের জুতা মেরে গলাই জুতির মালা ঝুলানো দরকার আর যে ভালো মানুষ দেলুয়ার হোসেন সাঈদি আজ জেলে হায়রে বাংলা দেশ,0,religion
তুই কে তাহেরী নামে বদনাম করোস তুই কি বুঝোস ইসলাম বিষয়ে,0,religion
ওরে খবিশ কোনো শয়তান নবির বেশ নিতে পারেনা।আর তুই একবার বলিস নবির মেয়ে ফাতেমাকে নাকি বিয়ে করছিস এখন বলছিস তোকে মানুষ নবির বেশে দেখে তুই কি বুঝিস যে তুই কি বলিস?আস্ত খবিশ একটা😠😠😠😠😠,0,religion
সময় আসবে যখন প্রতিটা নাস্তিক কান ধরে উঠ বস করবে। তাদের চামরা কেও তুলে ফেললে খুব খুশি হতাম।,0,religion
এই কাফেরের বাচ্চা মরনের চিনতা কর,0,religion
ওরা তো জানোয়ার যারা ওকে পীর ভাবে তারা আরো বড় জানোয়ার,0,religion
হুজুরের সৎ সাহস আছে প্রতিবাদ করার!! আর জনগন যেভাবে প্রতিবাদ করলো মাজার পূজারীর বিরুদ্ধে দেখে খুব শান্তি লাগলো মনে।এভাবেই এগিয়ে যাক ইসলাম আর ধবংস হোক মাজার পূজারী ভন্ডগুলার,0,religion
আল্লাহ তুমি সবাইকে বুজার মতো তওফিক দাও,0,religion
তারে থাপ্রা দিয়া বাইর করে দিলোনা কেন 😡😡😡,0,religion
কে কে মিজানুর রহমান আজহারী পক্ষে আছেন হাত তুলুন,0,religion
চার জনকে বলছি তুরা জাই করস আমার ইসলামের কিছুই করতে পারবি না নাস্তিকরা,0,religion
যারা আসলে তার মুরীদ কেউ তার আসল মুরীদ নন। সব সে টাকা দিয়ে ভাড়া করেছে। আর যারা বলে সে এমন করতে পারে এমন করতে পারে সব সে টাকা দিয়ে ভাড়া করেছে। কেউ আসেনি সৌদিয়া থেকে আর কেউ দুবাই থেকে। সব মিথ্যা বলে।,0,religion
উচিত কথা তো তাই গঁায়ে লাগবে সত্যকথার জন্য ম্যাডামকে ধন্যবাদ। একজন সত ও সাহসি নারি।,0,religion
আল্লাহ সবাইকে সঠিক বুঝ দান করুণ!,0,religion
আপনি নাজেনে হাফিজুরকে বন্ড বলেছেন তাই আপনার চেনেলে সাসক্রাব আছালাম উটিয়ে ফেলে ছি,0,religion
ভণ্ডামির একটা সীমা আছে তো সীমা লংঘন করে দিচ্ছে গিয়াস উদ্দিন তাহেরী ভাই কি মুসলমানের বাচ্চা এরকম ভাবে ছেসতেছে কেন পাগল হয়ে গেছে নাকি,0,religion
দেওয়ানগাভী,0,religion
যে কুকুরগুলা গু খায় তারাও তাহেরির মত ভণ্ডদের চেয়ে অনেক ভালো ছি ছি ছি এরা কি মরবোনা?,0,religion
আল্লাহ তুমি এই রকম মানুষদের হেদায়েত কর,0,religion
প্রচুর এভাবেই এগিয়ে যান এই ভন্ডদেরকে এভাবেই শায়েস্তা করতে হবে,0,religion
হেরে বি বাড়ীয়া তে আনছে কে হে এক বাটপার যে আনছে হে এক বাটপার হে বালের বক্তা হেরে ওলটা জুতা পেটা করা উচিত ছিল।,0,religion
আমার কলিজার টুকরা খাজা বাবা যিনি আজমীরে শুয়ে আছেন।।।।।,0,religion
যদি এই দেশে দেলোয়ার হোসাইন সাঈদীর মত একটা লোক দেশের সরকার হয় তবেই বাংলাদেশ নামক দেশটি বিশ্বে একটি মুসলিম দেশ হিসাবে পরিচিতি লাভ করবে । দেশ টা হবে সন্ত্রাস মুক্ত। আল্লাহ যেন সেটা সম্ভব করে আমিন।।।।,0,religion
বাংলাদেশের আইন নটম্বারের কারনে তারা এতো প্রস্রয় তাই আমরা সাধারন মানুষেরা তাদেরকে পতিহতকরতেহবে।,0,religion
তদের যেমন শাহস আছে সব ভন্ডরা এক হয়ে আমাদেরও সাহস আছে শালা ভন্ডামী করস মাজার মানিস না,0,religion
আল্লাহ্ তুমি আমার দেশের সব মানুষের হেদায়েত দাও,0,religion
হুজুর এগুলো ভন্ডামি জিকির কই পাইছেন কুরআানে আছে কী?,0,religion
এইসবগুলা ভন্ড হচ্ছে দাজ্জালের দালাল,0,religion
আল্লাহ পাক তাদের উপর গজব ফেলুক,0,religion
মাজার পূজারী গোলাকে ধরে হাত পা বেঁধে জুতা বাইরে বাইরে বাইরে তে নাকে মুখে দেয়া জন লালা বাইর হয়ে যাবে তখন তাদের বাবা ঠাকুরের কাছে নিয়ে ফালায় দিতে হবে,0,religion
বন্ড পাগলের কথা,0,religion
শাহজালাল রঃ শাহপরান রঃ এর মাজারে অহরহ গাজা খায়। উরুশের নামে নারী পুরুষের অবাধ মেলামেশা চলে। প্রমান নিতে চাইলে চলে আসেন সিলেটে আমি সিলেট শহর থেকে বলছি।,0,religion
বাল পাকনায় কয় কি,0,religion
আল্লাহ্‌ কি কমু আমাকে খমা করু।,0,religion
নাস্তিক বাংলার মাটিতে থাকতে পারবেনা।,0,religion
আমাদের হুজুর রা প্রমাণ ছাড়া কথা বলে না বেদাত ভন্ডরা জেনে রাখ 💪💪,0,religion
খলিফাকে কাটগরায় দাড় করানো টা ঠিক হয় নি। মামুনুল হক ভাই আপনি উচিত কথা বলেছেন।,0,religion
প্রকৃতপক্ষে আব্বাসি একটা ভন্ড হুজুর,0,religion
যারা রং তরিকার চরকি গুরাচ্ছ আল্লাহর কসম করে বলছি বেইজ্জত হইয়া মরবি। তোদের নামাজ পোশাক এজিদের ছিন্ন। স্রতাগন দেখনা আহলে খবিছের ঢ্যনেল বন্ধ হয় নাই।,0,religion
এইটা খুব বেশী সাহসিকতা👏👏,0,religion
কুকুরের বাচ্ছাটাকে বাংলাদেশ থেকে বের করার জন্য সবাই ঐক্যবদ্ধ হউন,0,religion
নাস্তিক কোথাকার,0,religion
ইসলামিক ভিডিও পেতে এই চ্যানেলটিকে সাবস্ক্রাইব করে রাখুন। দ্বীনি ভাইয়েরা নামাজ পড়ার চেষ্টা করো আল্লাহকে দেখে ভয় করো ইনশাল্লাহ আমরা জয়ী হবোই হবো। চ্যানেলটি তে হাত বাড়িয়ে দিন দ্বীনি ভাইয়েরা অন্যদিনে ভাইকে দ্বীন প্রচারের জন্য এই চ্যানেলটি আমার এই চ্যানেলে একটু সাবস্ক্রাইব করে রাখ অনুরোধ আর বেল আইকনটি চেপে দিবা,0,religion
সালা তুই হলে কেয়ামতের আলামত। শিশু বক্তা কেয়ামতের আলামত। তুই আরেক জনের গিবত করছ তকে আল্লাহ ছাড় দিবেন না,0,religion
ভন্ডো,0,religion
এখানে আলেমদের আসা উচিত নয়,0,religion
গিয়াসউদ্দিন তাহিরি হুজুর আল্লাহর রহমতের ভান্ডার আল্লার নেক আলিম আমিন,0,religion
কাদিয়ানীরা ও দেওয়ানবাগি একই শয়তান তারা জাহান্নামি।,0,religion
আল্লাহ তাআলা যেন এই দাতজাইল দেরকে সঠিক ইসলাম লাইনে হেদায়েত দান করেন আমীন এর বিঝি আমার কাছে বলার নাই,0,religion
চার টা উন্নত জাতের বাস্টার্ড।,0,religion
নাস্তিকেরর ধ্বংস হউক,0,religion
দেওয়ানমাগি ত কাফের। তারে জন্ম দিসে কোন ইহুদি হবে। নয়ত এদেশে তার মতো ভণ্ড কেমনে আসলো,0,religion
মাশা আল্লাহ আলহামদুলিল্লাহ টিক কথা বলে চেন অনেক সুন্দর আলোচনা আমরা খুঁজি হয়েছি আপনাকে অনেক ধন্যবাদ আলহামদুলিল্লাহ ভালোই বুঝার চেষ্টা করি আমিন আমিন আমিন আল্লাহ পাক হেদায়েত দান করুন আমিন আমিন আমিন আল্লাহ,0,religion
ভাই কাদিয়ানী কাফের কাফের কাফের কাফের,0,religion
কসটো পাইলাম,0,religion
দেওয়ান বাগি কে জুতা মারো,0,religion
অপেক্ষা করছিলাম।,0,religion
ভাই আহসান হাবিব পিয়ার কোথাই,0,religion
তোমাদের। বিচার। আল্লাহ। করবে,0,religion
মানুষের পেট থেকে এইটা জানোয়ার বের হয়ছে,0,religion
ফেতনাবাজ তোমরা। ফেতনা ছড়ায় কি লাভ?,0,religion
এক ভাই বলেছিল্ল মনদির নাকী কোন্ন ক‍্যাছজমিন জমিন হয়না ভাই আপনি ভোলবাবছে জদি হয় হান্দি দের জমিণ হয় দহেল্ল অবশু আপনি বান্নাভে,0,religion
ইয়া আল্লাহ্ তুমি হেদায়তের মালিক,0,religion
যে যাই বলে বলুক অাপনি চালিয়ে যান সুন্নি সমাবেস অাপনার সাথে অারোও,0,religion
সমকামী হুজুর,0,religion
সব মাজারে গাজা খায় উজুর সও বলচেন,0,religion
আগে নিজে ভালা অই পরে অন জনকে খারাপ কই,0,religion
আই ফোন বিকরি করা হবে এস,0,religion
তাহেরি তুমি কি মনে কর নিজেকে। তোমার থেকে অনেক বড় আলেম মুফতি মাওলানা আছে।,0,religion
ফাইন,0,religion
তাহেরি এবং দেওয়ানবাগী ফাঁসি দেওয়া উচিত,0,religion
এই ভন্ডটারেই আপনাদের নিতে হইলো??? আব্দুর রাজ্জাক বিন ইউসুফকে চোখে দেখেন না?,0,religion
ছিঃ বাংলাদেশে কি হয়তাছে এসব আমরা মুসলিম দেশ হিসাবে সম্নান করি,0,religion
এই বন্ড কে গন দুলাই দিয়ে পুলিশে দেওয়া হক?।,0,religion
চার জনকেই দেখতে পুরাই সয়তানের মতন নাস্তিক এর বাচ্চা গুলি,0,religion
তুই ফাযিল,0,religion
চিচিচি তোদের মত কুলাঙ্গারের জন্য আজ এই বাংলাদেশের এই অবস্থা ওয়াজ করতে তুই ওয়াজের কি বুঝস,0,religion
ধন্যবাদ ভাই ভন্ডদের মুখোশ উন্মচন করে দেওয়ার জন্য,0,religion
নাওজূবিল্লা আল্লাহ আপনাদের কে হেদায়েদ দেক,0,religion
এদের কে জোতা দিয়ে পিটিয়ে মেরে ফেলা উচিত।।,0,religion
এই ধরনের মাজার পুজারী ভন্ড ষ্টেজে উঠলো কেমনে? এলাকা থেকে একে জুতা পিঠা করে তাড়িয়ে দেওয়া উচিৎ।,0,religion
ছিঃছিঃ,0,religion
আমির হামজা তরে জদি পেতাম জুতা পিঠি করতাম,0,religion
তাহেরিকে সামনে পেলে জুত দিযে পিটানর দরকার,0,religion
খাজা বাবার কিযে হবে আল্লাহ ই জানেন নিজের আমল এ নিজেকে পার হতে হবে আপনাদের খাজা বাবা আসবে না,0,religion
আমির হামজা তুই কি কিসের মুফতি তুই কলেজে পড়ালেখা করচোচ তুই ইসলাম সম্পর্ক কি জানিস,0,religion
দেওয়ান বা গিরে জুতু পিটা করে মেরে পেলা হউক।।,0,religion
আসসালামু আলাইকুম হুজুর আপনার ওয়াজ বাংলাদেশের মানুষের মন উজাড় করেছে,0,religion
কিছুই করার নাই ভাইয়া আমরা আপনার প্রতিবাদ করলে কি হবে সরকার তো প্রততিবাদ করতেছেনা,0,religion
আলেম সাহেব এসব বোকা লোকদের সাথে ডিবেটে বসে লাভ নাই,0,religion
আললাহু আকবার আজানটা খুব সুন্দর,0,religion
ভাই।। অনেক ভালো,0,religion
এদের বিরুদ্ধে ধর্ম অবমাননার মামলা হয় না কেনো ?,0,religion
ভাই এরাই দেশের বড় ভন্ড,0,religion
আইয়া আপনার ভিডিও টি খুবই ভাল লাগে,0,religion
নিত্যনতুন ওয়াজ ইসলামী সংগীত ও যেকোন ইসলামী ভিডিও পেতে আমাদের চ্যানেলটি সাবস্ক্রাইব করুন।,0,religion
নাস্তিকদের সামনে কেন যায় হুজুররা,0,religion
এই সালাগো চুলের দলিল আর মিস্টি কাওয়ার দলিল ছারা কোনো পুঁজি নাই,0,religion
আল্লাহ তুমি ভন্ডদের হেদায়েত দান করুন আমীন,0,religion
আপনার বলার ভঙ্গিমা খুব একটা সুন্দর নয় অন্যান্য ইউটিউবার থেকে শিখুন ভাল করতে পারবেন,0,religion
সিজদাহ্ দিলে আল্লাহ কে দিব কাওকে অনুসরণ করলে রাসুলুল্লাহ সাঃ করবো আমরা আল্লাহ গোলাম রাসুলুল্লাহ সাঃ উম্মত,0,religion
আরে ভাই এ তো দুর্দান্ত ! অনেকদিন ধরেই মজার বাংলা কার্টুন খুজছিলাম ! আজ আপনার মাধ্যমে কার্টুন পেয়ে গেলাম ! তা ভাই এরকম কার্টুন আরো পাব কি ? মাঝে মাঝে তো একটু বিনোদনের প্রয়জন হয় তাই না ?,0,religion
হু হু হি হা হা হা হা হা হা হ,0,religion
আববাসি কে জুতা দিয়া পিটায় নাই তার কপাল ভাল,0,religion
বন্ধুো,0,religion
তুই তো নবি থেকে বের হয়ে গেছো হালার পুত,0,religion
পীরের নামে অনেকে ব্যবসা করে পেট চালাচ্ছে। তাদের ভন্ডামিতে পা দিলে ধ্বংস হবে।,0,religion
একাই চিল্লায় জনগণ কই,0,religion
তুই যে ভন্ড কুলাঙ্গার তর কথায় তুই প্রামাণ দিলে। এই ভন্ড জাহিল হজ্জে গিয়ে মাথা মুন্ডানো কার সুন্নাত বল ? আর তাবলীগ নিয়ে আজেবাজে মন্তব্য করছ কেন ? তাবলীগ ওয়ালারা কি মাথায় পাগড়ি বাঁধে না ?,0,religion
গুলো নাস্তিকরা দিছে👿,0,religion
এইসব নাস্তিকদের সাথে হযরতের বসাটাই উচিত হয়নি।অন অতিলমবে এই নাস্তিকদের ফাঁসি চাই। দিতে হবে ☝️,0,religion
হেতার জম্ন হল কবে আবার ওয়াজ করে। হেতার কথা শুনলে মনে হয় বয়স,0,religion
এমন নারী পৃথিবী থেকে বের করে দিতে হবে,0,religion
এই চার নাস্তিক কে আল্লাহ এমন সাস্থি প্রধান করবেন যা দুজোখের সব বড় সাস্থি হবে,0,religion
হাজারটা নাস্তিক কাফের ইহুদি বেদ্বীনের সঙ্গে লড়াই করার জন্য একজন ঈমানদার ব্যক্তিই যথেষ্ট ইনশাআল্লাহ্।,0,religion
মিজানুর রহমান আজহারী সঠিক।যখন নবীর উপর হেরা গুহায় কুরান নাজিল হচ্ছিল তখন জিব্রাইল আঃ বলেন আপনি পড়ুন। আমার নবি বলেন আমি পড়তে জানিনা,0,religion
এদের ফাসিচাই,0,religion
হা হা হা 😃😃😃😃😃😃,0,religion
হালার পোর ফোন নাম্বার টা কেউ দিতে পারবেন?,0,religion
এই ভন্ড দেওয়ান বাগী কোন খুটিঁর জোরে দিব্যি টিকে অাছে!,0,religion
একে দেশ থেকে বাহার করা হক,0,religion
মিজানুর রহমানের যে ভণ্ড বলে সে যারোজ,0,religion
বেয়াদব থাপরাইয়া দাত ফালাইয়া দিব,0,religion
হুজুর তোমার কাছে আমার প্রশ্ন কোনো হাদিস কোরআনে আছে কি কারো গিফত করা পারলে নতুন কিছু বলো কারো গিফত করা ভালো না,0,religion
শিশু বক্তা দিয়ে ওয়াজ করাই না আর এটা ভুল ওর নাক চাপ দিলে দুধ বের হয় য়া বলবে সব মুক্ত আর এটা কিয়ামতের আলামত,0,religion
ইসলামে পীর বলতে কিছু নাই !পীর ফার্সী শব্দ এর অর্থ হল মুরব্বী। যা কিছুর চাওয়া আল্লাহ দরবারে চাইতে হবে এবং আল্লাহ পাক সব বান্দাকে সমান চোখে দেখে।আল্লাহ পরে নিজের মা বাপের খেদমত করতে হবে।পীর কে গোসত পোলাও আপেল আঙুর কলা দুধ না খাওয়ে। নিজের মা বাপকে খাওয়ানো জররী।কারন মা বাপের দোয়া আল্লাহ সরাসরী কবুল করে।পিতামাতার খেদমত করলে জান্নাত নিশ্চিত্বব।এটা আমার নবী সাঃ বলে গিয়াছেন এবং সহীহ বোখারী মুসলিম শরিফ তিরমিজি হাদিসে বর্নিত।তাই পীর নামক ভন্ডদের ত্যাগ করে আসুন আমরা মাতাপিতার যত্ন করি এবং পাচ ওয়াক্ত নামাজ পড়ি সৎ পথে চলি গরীবকে সদকা দান করি আত্মীয়দের সাথে ভাল আচরন করি।তবেই আমরা জান্নাতে যেথে পারব।আর দেওয়ানবাগী হল মুরতাদ জালেম ফাসেক।যদি দেশে প্রকৃত ইসলামি আইন থাকিত। তাহলে এর ফাসী হত।,0,religion
এরা শুধু নাস্তিক নয় স্পষ্ট মুসলিম বিদ্ধেশী এদের মুসলিম প্রধান দেশে থাকতে দেওয়া আর নিজের পায়ে কুড়াল মারার মধ্যে কোন তফাত নেই ।,0,religion
তক্তার বাচ্চা তুই নাসির নগর আসিস।,0,religion
আল্লহর গজব পরুক,0,religion
এই নাস্তিকদের সাথে আপনি কেন গেলেন আপনাকে ওরা কথা বলতে দিবেনা মামুনুল হক সাহেব।,0,religion
ইহুদির দালাল,0,religion
কিছু কিছু জুতার বাচ্চা আছে না বুঝে ঠিক ঠিক করে,0,religion
এই কুকুর দের সাথে কেন মুফতি সাহেব কথা বলতে এছেসেন,0,religion
তাহেরি ভন্ড ও,0,religion
এমুল্লা ওহাবি হারামজাদা ওলি আল্লাহর দুশমন জালিম জুতামারার দরকার,0,religion
হুজুর ঘাড় পর্যন্ত রেখেছে আপনি কতটুকু রেখেছেন আপনি মাপ দিয়ে দেখেন আপনার টা তো আরো অনেক লম্বা বে আকল।,0,religion
চার নাস্তিকের বাংলার জমিনে জানাজা জেনো কোনো আলেম না পড়ায়। এদের লাশ জেনো শিয়াল কুকুর দিয়ে খাওনো হয়। আল্লাহ তুমি বাংলার মানুষকে দেখিয়ে দিও।,0,religion
মুসলমান দেখো রাখো ইসলাম কাউকে আঘাত করে না বরং আল্লাহপাক এর পবিত্র কুরআন এর বাণী শুনিয়ে দিলটাকে ঠান্ডা করে দেয় সুবহানাল্লাহ,0,religion
মারহাবা অনেক সুন্দর,0,religion
মাশা আল্লাহ। সুন্দর।,0,religion
এই শিশু বক্তা নাম্বার ওয়ান বেয়াদব তাহেরী হুজুর ওর চেয়ে বয়সে অনেক বড়,0,religion
আল্লাহ যেনো তাকে হেদায়েত দান করেন।,0,religion
কমেন্ট এ কি জানতে চান মাও মিজানুর রহমান সাহেব হুজুরকে কি মানুষকে ভন্ড বলতে বলছেন?,0,religion
মিজানুর রহমান আল আজাহারী রাইট,0,religion
এই ধরনের প্রচার থেকে বিরত থাকুন। আপনাকেও নাস্তিক ভাবতে বাধ্য হব,0,religion
ওই যে বক্তা সাথে তরক করলো ওই বুড়ো গেজা খেয়েচে না হলে এতো সুন্দর ওয়াজ বন্ধ করলো,0,religion
এতো কষ্ট করে লেখা পড়া করা আলেম কে নিয়ে কথা বলাটা ঠিক না। সালা হাদীস সম্পর্কে তুই তো কিছুই জানিস না গতিকে এই সব শিশু বক্তা নিয়ে আপনার অনুষ্ঠান করবেন না । আমি আসাম কামরুপ জিলা থেকে বলছি। আমার নাম আমিনুল শেখ।,0,religion
বেয়াদব তুই আললা পাকের ভুল নিয়ে আলোচনা করলে যিনি দুনিয়া তৈরি করতে পারেন তিনি কখনো ভুল করেননি ।,0,religion
ভাই আপনার মোছগুলো আরো একটু ছোট করলে ভালো হবে।,0,religion
ভিডিও টা লাইক দেয়া আমার জন্য ফরজ। 😆 😆,0,religion
আমির হামজা একজন সত্যি খাঠি আলেম,0,religion
আল্লাহ ওদের হেদায়েত দান করুন বা গজব দিন,0,religion
যে যেখানে বশার জোজ্ঞো না তাকে শেখানে বশালো বাচ্চা পোলাটার কথা ফালতু মনে হলো।। এই সব হচ্চে কিয়ামতের আলামাত। তুমি তোমার আম্মুর দুদু খেয়ে আগে বর হও,0,religion
ভাই আমার মনে হচ্ছে। এই রকম ইমান হারা না হয়ে। ভারতের হিন্দু হাতে মরা ভালো। ভারতে এই রকম মাল আছে। কিন্তু ওদের কাছে বাচ্চা। আমরা অনেক ভালো আছি,0,religion
হেফাজতের সাথে জামায়াতের কি সম্পর্ক।।। মুরগা চুর,0,religion
কুত্তা,0,religion
তাহেরির একটা ফসমের যোগ্য হোওনাই,0,religion
আমি এক মত,0,religion
আজ খুবই ভালো লাগলো অবশেষে সেই দিন এলো আর সেইটা হল ভন্ড দেওয়ান ভাগী র অপকর্ম নিয়ে ও নাস্তিককে নিয়ে করলেন,0,religion
মামুনুল হক বা যেকোনো ইসলামপন্থীরই উচিৎ হবে এধরণের গাজাখুরীদের সাথে টকশো তে না যাওয়া। তিনটা শয়তান বসছে পাশে আর উপস্থাপিকা ত আরেক ভারতীয় এজেন্ট। সবাই কে সময় দিবে পর্যাপ্ত আর মামুনুল হকের বেলায় কম।আর জনের বিপরীতে একজন কেনো? এটা কি উনাদের হিপোক্রেসি নয় ?জ্ঞানপাপী ভন্ডদের বয়কট করাই উচিৎ।,0,religion
এরা এমনই গন্ড মূর্খ যে মামুনুল হক বলতেছেন কোন রাষ্ট্র আমাদের আদর্শ নয় আমাদের আদর্শ হল কুরআন হাদিস তারপরও বলে একটা রোলস তো থাকতে হবে আরে গর্দভ কুরআনের চেয়ে বড় রোলস আর তুই কি চাস?,0,religion
ফণ্ড,0,religion
ওকে জুতা পিটা করা দরকার।,0,religion
মানুষ না জানোয়ার মুখে দাড়ি নাই মাথাই কাপড় নাই ওরা ইসলামের কি বুজে ।।পানি খাওয়ার সময় মুচে লাগলে পানি খাওয়া হারাম ।সালা তো তাই যানেনা ।।।।আবাল সালারা,0,religion
তুইএটাজানূআর,0,religion
অনেক সুন্দর হইছে,0,religion
যারা দিসে তারা দেওয়ান বাগির ভক্ত। 😡😡😡,0,religion
কোনটা অপমানিত কোনটা সম্মান সেটাতো তুই চিনিসনা তোকে কে বলছে ইউটিউব চালাতে,0,religion
তাদের রুহানি ফায়েজ দোয়া চাওয়া জায় সব মুমিনের রুহানি দোয়া চাওয়া জায়,0,religion
চারটা কুকুড় একজন মানুষ,0,religion
ভাই সব ঠিক আছে কিন্তু আমার কথা হলো যে মিজানুর রহমান আজহারী হুজুর যে বলছেন নবীজির বুক টা ছিলো উচু পেটটা ছিলো চাপা। এই কথা টা পবিত্র কুরআন বা কোন হাদিস শরিফ এ নেই। এটা উনি ভুল বলেছেন হে আমিও মানি যে উনি অনেক কিছু জানেন। কিন্তু বানোয়াট কথা কেনো বলেন??,0,religion
মিজানুর রহমান আজহারী কে নিয়ে টিক টক করা ঠিক হয় নাই আপনাদের কাছে অনুরোধ হুজুরদের নিয়ে টিক টক করবেন না,0,religion
ধন্যবাদ ভাই আপনাকে এই ভন্ড তাহেরী কে নিয়ে কথা বলার জন্য সে আসলে মানুষ রুপে জানোয়ার,0,religion
এখানে মাজার পূজার কি হল,0,religion
অপেক্ষায় ছিলাম,0,religion
এরা কখনোই মুসলিম নয়। মুসলিম লেবাসে অমুসলিম। মুসলিমের বদনাম করার জন্যই এদের জন্ম।,0,religion
এইসব এডিটিং করা ভিডিও বানিয়ে ছাড়িবেন না বিয়াদব,0,religion
সরকার প্রশাসন কেন এদের বিরুদ্ধে বেবস্তা নিচ্ছে না,0,religion
তুরা হলি দলের এক দল যেমন রশুনের গুরা কিন্তু একটি এর কুশ থাকে চোতুর দিকে চুটো বোরো অনেক গুলা থাকে তুারাও তেমন,0,religion
বহু ভন্ড হুজুর ও আছে তাই বলে সকল হুজুর খারাপ না। তেমনি এভাবে সকল ওলিদের কে খারাপ বলা ঠিক নয়। আলেম ওলামাদের এভাবে বিতর্কিত ওয়াজ করা ঠিক নয়।,0,religion
মাজার পুজারি,0,religion
ওয়াজ নাকি গীবত করছে এটা ওয়াজ কয় না অন্যের এড দিতে আসছে।,0,religion
এসব ভন্ডামী,0,religion
ভাই তো গলা অনেক সুন্দর,0,religion
এদের কে মেরে ফেলা উচিত,0,religion
যারা এরে আনছে তারা কি ঘাস খায়,0,religion
মানুষ হবি না,0,religion
ধর্মটা সম্পূর্ণ মিথ্যা উপরে চলছে,0,religion
এদের জিকির শুনে সয়তানও ভয় পাইবো,0,religion
আমি নিজে দেখেছি মাজারের উপলক্ষে নাচ গান হচ্ছে,0,religion
দেওয়ান বাগিকে ঢাকার জিরো পয়েন্টে ফাশি দেওয়া হোক তাহলেই এই দেশে ইসলাম কয়েম হবে,0,religion
আরে শালা বলছি কি আর তুই শুনছো কি তোর মত কাফের আল্লাহ যেন মাফ না করে,0,religion
এই চারজন চোরকে জুতা পিটা করা দরকার !,0,religion
এও কোলংগার ছেলে৷,0,religion
ভাই আগে তুমি ঠিক হও তার পরে ইসলাম প্রচার করো ধন্যবাদ সবার কেমন লাগেছে সেটা জানি না কিন্তু আমার মনে হচ্ছে তুমি ইহুদিদের দালাল,0,religion
দেওয়ান বাগী তোরে কপালে জুতোর বারি,0,religion
আমি ভাৱত থেকে বলছি ?আমি নাস্তিক লোপা ৱহমানেৱ ফাঁসি চাই।,0,religion
শিশু ভক্তার ওয়াজ শুনা হারাম,0,religion
বিখ্যাত নয় কুখ্যাত জন নাস্তিক,0,religion
শিশু বক্তাদের বয়কট করুন। ডিসলাইক দিলাম,0,religion
যারা ডিসলাইক মারসে এরা সবাই দেওয়ানবাগির পাগলা ফ্যান। এদের কারো জন্মের টিক নাই,0,religion
তোরে আল্লাহ যে কি করবে আল্লাহই জানে,0,religion
মুরিদের লাথি মেরে মেরে ফেলা উচিত।,0,religion
আমি ও ভালোবাসি,0,religion
সামান্য এটা কথাৰ কাৰণে মাৰামাৰি এইটো হ ল ইছলামী নীতি। খুব লাজৰ কথা হৈছে। ধৰ্ম হ ল মানুহৰ মনৰ কথা।অইনে জুলুম কৰাৰ কিদৰকাৰ।,0,religion
আল্লাহ তার বিচার করুন,0,religion
এদের কে যেন জুতা মারা উচিদ,0,religion
কিতা দিয়া কিতা তুলনা দেশ আব্বাসী কে জানাস নি তুই যদি জানা তোর মারে জিগা ইস তোর বাপ কে তোর বাপ কে হারামজাদা,0,religion
ভাই আপনাকে ছেলুট,0,religion
কামিল পাশ করে একজন এইট পাশের মত কাজ করলে চলবে না লাফালাফি দাপাদাপি কি বলে জিগির করে সেটাও তো বুঝিনা আমির হামজা ভাই আপনি এগিয়ে যান ইনশাল্লাহ,0,religion
কমেন্ট গুলা সবাই ভালো ভাবেই লেখেছেন পড়ে অনেক ভালো লাগলো,0,religion
হুজুরকে আল্লাহু নেক হায়াত দান করুক এবং মাঝার পুজারি কে জুতা মারার জন্য হুজুর কে ধন্যবাদ,0,religion
আল্লাহ জদি রাজি থাকে তাহলে তাহিরির কিচৈ হবেনা,0,religion
পাগলের সংলাপ আল্লাহ আল্লাহর রাসূল যেভাবে জিকির করার নির্দেশ দিয়েছে সেইভাবে জিকির করুন,0,religion
দেশে ইসলামের শাসন থাকলে এতদিনে কুলাঙ্গার গর্দান হয়ে যেতো,0,religion
কি আর বলবো এদের কথা,0,religion
শালার মুখে জুতা মারাম শালা নাস্তিক এর বাচ্চা,0,religion
ইসলামে তো শুকর হারাম তাহলে এই শুকর দেশে বিরাজ করে কিভাবে মাথায় আসে না 😖,0,religion
এই খানে দেখি ওহাবিরা বেশি।,0,religion
হুজুর সঠিক কথা বলছে,0,religion
ভাই হালারে থাপরাইতে মন চাইতেছে,0,religion
এইসব নাস্তিকদের বিচার উপর ওয়ালায় ঠিক করে রেখেছেন । এবং অতি শিগগিরি তারা তাদের শাস্তি যেন পায় ।। আর আমরা যেন তাদের মুখ থেকে তওবা করার ভিডিও দেখতে পায়।সেই কামনাই করছি ।,0,religion
হুজুর এই শয়তানদের কাছে যাই কেনো,0,religion
আল্লাহ্ তুমি এই নাস্তিকদের কে খেদায়েত করেন আমিন।।,0,religion
আফসোস লাগে যখন দেখি অনেক শিক্ষিত ধনী লোক এই কুজাতদের পিছনে লাখ লাখ টাকা খরচ করে। এই ভিডিওগুলা কখনই তাদের নজরে আসবে না। চ্যানেলটির ভাইয়াদেরকে বলছি আপনি যেটাই করেন সব ক্ষেত্রে হেটার্স থাকবেই।,0,religion
সোনা আচে তর চ্যালেন তুই তাহেরি হজুর কে চ্যালেন করছ তুই কেনো চ্যালেন করছ পারবি চ্যালেন কইরা,0,religion
কিয়ামত আর বেশি দেরি নাই!এই সব শিশু জালিম গুলো মানুষের ঈমান নিয়ে যাবে!আর এইগুলো ও মানুষে শুনে!মানুষ ঈমান নিয়ে মরতে পারবে না!,0,religion
মুরগি চোর কবির। মরে দেখ বাশ রেডি করে রেখেছে আল্লাহ,0,religion
‌‌কাফের কাকে বলে সেটা আগে জানুন,0,religion
ভাই আপনি তো নিজেই শেয়ার মেয়েদের বুকের পাটা দশ হাত করে দিচ্ছেন আবার আমাদেরকে বলছেন ইসলামের অপপ্রচারকে শেয়ার করতে পরেরবার এইসব ভিডিও ইউটিউব এ আপলোড করার আগে ঈদের মার খাওয়ার ভিডিওটাও আপলোড করবেনতবে শেয়ার করেছেন যাতে সবাই দেখতে পারে নাস্তিকের পরিণতি হয়তো একজন নাস্তিকের অপপ্রচার করবে আর আপনি ইউটিউবে আপলোড করে আমাদেরকে বলুন শেয়ার করতে কি,0,religion
ভাই আপনে এগিয়ে জান এসব বন্ড মাজার পূজারি কথায় ভয় পাবেন না,0,religion
ভাই আমি ছাড়া এই ভিডিওর আসল মানে এবং উদ্দেশ্য কেউ বুঝে নাই!,0,religion
ইল বাবা,0,religion
আমির হামজার কথা একদম সত্য,0,religion
পাগল সব। কাজ কর্ম নেই,0,religion
এদেরকে পাইলে জুতা মারতাম,0,religion
মাননীয় প্রধানমন্ত্রী শেখ হাসিনার এবং ধর্ম মনএীর কি এগুলো চোখে পড়েনা নাউজুবিল্লাহ,0,religion
তাহসিন ভাই আল্লাহ আপনাকে ভালো রাখুক! এই দেওয়ারবাগীকে আমাকে মেরে ফেলতে ইচ্ছা হই,0,religion
এরা সাধু,0,religion
মাজার সর্ম্পকে জানতে চাই ? ওরা ভন্ড বলে আমাদের,0,religion
সাবধান আললাহর অলিরা অমর। তাদের সাথে লাগতে যাওয়া মানে আললাহর সাথে যুদ্ধ ঘোষনা করা। দেওয়ানবাগী আললাহর অলি। মা ফাতেমা কে নিয়ে এটা মিথ্যা বানোয়াট কথা প্রচার করা হচ্ছে। বছর আগের মা ফাতেমাকে তিনি বিয়ে করেন কিভাবে। তিনি নিজেইতো তাকে মা ফাতেমা বলে ডাকেন। নিজের সত্রী কে কি কেউ মা ডাকে নাকি। এরা সব বোকার সর্গে আছে। মিথ্যা অপপ্রচার করছে।,0,religion
অনুষ্ঠান শেষ করা উচিত ছিল,0,religion
আমার ও খুব প্রিয় মিজানুর রহমান আজহারির।,0,religion
এটা কি শয়তানের জিকির,0,religion
বশেন বশেন এ,0,religion
এধরনে আলেমদেরকে বয়কট করা উচিত,0,religion
ফালতু ছেলে,0,religion
মইরা দেখ খাজা বাবায় খাজা খাবাইবো,0,religion
সরকার কি ঘাস কাটে ওদের পাশি দিতে পারেনা নাকি ওনিও এমন,0,religion
অসুস্থ দেওয়ানবাবা👠👠 অরে কেউ পাবনায় পাঠায় না কা😑 ভাভা যায় এগ্লা😕😕 কাফের কত্তগুলা💩💩,0,religion
এমন ভিডিও আরো চাই এটাই মুখোশ খোলার পথ,0,religion
একে ফাসী দিতে হবে,0,religion
তাহিরিরে দেখলো আমার ভাদাইমার কথামনে পরে,0,religion
ভাল লাগলো,0,religion
শত হাজার বার বলতে পারি গিয়াসউদ্দিন তাহেরি একটা আস্তা বড় শয়তান,0,religion
আরে ভাই আপনাদের বুঝতে ভুল হয়েছে কারন মিজানুর রহমান ঠিকিই বলছে,0,religion
মোচগুলো দেখলে মনেহয় জুতোপালিশ করার মুচি💃💃💃,0,religion
হে আল্লাহ যদি তার কপালে হেদায়েত থাকে তাহলে তাকে হেদায়েত দান করো আর না হয় তাকে ধ্বংস করে দাও।,0,religion
দুধের মাথায় হাত দিয়া কি দেখে,0,religion
ওয়াজী নাকি শয়তান তার আচরণ দেখুন। বেয়াদব,0,religion
আল্লাহ এরকম নাস্তিকদের কঠিন শাস্তি দিন আল্লাহ,0,religion
আসসালামুয়ালাইকুম তাহসিন ভাই🥰🥰 কি ভিডিও বানিয়ে চেন ভাই !দেখমু কি নাঊযুবিল্লাহ বলতে বলতে সেস ? আরও যতো এইরকম ভন্ড আছে তাদের নিয়ে ও কথা বলুন মানুষ উপকৃত হবে!! ধন্যবাদ ভাইজান 😍😍,0,religion
শয়তানবাগী!,0,religion
আজাহারি খুব ভালো,0,religion
নাউজুবিল্লাহ।কত মানুষ এর পাল্লায় পরে ঈমান হারায়,0,religion
আল ফেতনাতু আসাদ্দু মিনাল কতল। ফেতনা হত্যার চেয়ে জঘন্য। বেটা ফেতনা করার আর কিছুই পাওনা। সালা বে আক্বল আদ্মি,0,religion
গিয়াসদ্দীন আত তাহেরী সে একটি কুক্ষাত বন্ড এবং নটত্বকী এতে কোনো সন্দেহ নাই আমার ।। গিয়াসদ্দীন আত তাহেরী এই নংরামী ছেড়ে সোজা সাপ্টা ভালো হয়ে যা। আর না হলে কঠোর বিপদের সম্মুখীন হইতে হবে ।।,0,religion
এদের জানাজা যে ইমাম পরাবেন তাদের ও নাস্তিক বলতে আমার বিবেক হয়তো বাধা দিবেনা।,0,religion
এখন থেকে কাপড় কইল্লা গেছে,0,religion
মাজার পুজারিকে ইচ্ছামত পিটা,0,religion
এই হুজুর কে সৌদি আরবে পাঠাইয়া দেন সঠিক বিচার হইবে,0,religion
আমার চ্যানেলটি নতুন প্লিজ সাবস্ক্রাইব করে পাশে থাকুন,0,religion
ওর শিখার বয়স এখনো শেষ হয়নি। দয়া করে ওকে শিখতে দিন। ঠিক সময়ে সেও তাহলে সঠিক শিখখা দান কোরবে।মুখসতো করা কিছু শবদো দিয়ে দিনের সঠিক শিখখা সমভব নয়।আশা করি মতামতে সবাই একমত হবেন।।।।,0,religion
এরা কী মুসলিম? না আন কীছু,0,religion
এর মানে কী 😱😱😱😱😱😱😱😱😱😱😱😁😁,0,religion
ভন্ড তাহেরি তুই আর একটা ভন্ডামি কথা বললে জুতার বাড়ি মারবো তোকে বেয়াদোপ মাঝারে তোর বাপ সুয়ে আাছে তোর বাপ কে আমাদে কোনো দরকার নাই কারন আল্লাহ বলেছে মুমিন দের জন্যো আমিই যতেষ্টো,0,religion
ভন্ডামি বাদদেন,0,religion
গিবত করছ শালা,0,religion
ভাই এদের মধ্যে কি করা লাগবে এখন বলেন তো,0,religion
কিছু মাজারে চলে গাজার অাসর অার ভন্ডামি,0,religion
এর জন্য আরেকটি এবং বাংলাদেশি দরকার,0,religion
বাই সব বুয়া,0,religion
আপনার জলে কেরে হেতান সুন্দরি তায় আমরা পাঁচ দশ দিয়ে দি। কি সুন্দর নাচ। হায় রে মেরে মর জাওয়া। জুম্মা চুম্মা দে দেয় চুম্মা।,0,religion
এই মাজারি পুজারির কারনে আমাদের আজহারি সাহেব কে মানুষে গিনার চোখে দেখে আল্লাহ আপনি আব্বাসি হেদায়েত করেন,0,religion
কাফের গাব্বাসি জিলাপি আলাউদ্দিন বসেন বসেন তাহেরি নক্সাবন্দি বস্তাবন্দি রেজভি গজভি আহলে সিন্নি কবর পূজারি মাজার ব্যবসায়ি এদের চাকরি করার যোগ্যতা নেই ব্যবসা করার পলিসি নেই তাই অশিক্ষিতদের ঠকিয়ে গিবত করে দিনযাপন করে।,0,religion
তাইলে ফাঁসি চাই তাহেরের ফাঁসি চাই তাহেরের ফাঁসি চাই,0,religion
তুই একটা ভন্ডা,0,religion
নাম ধারিদের ধরিয়ে দিন আইনের আওতায় তাতেই ইমানদারি সবাই রেহাই পাবে এবং শান্তি পাবে আল্লার রহমত নাজিল হইবে ইন্সায়াল্লা,0,religion
এরা তো জাহান্নামে যাবে,0,religion
এগুলো তো মুসলমানদের মধ্যে পড়ে না এগুলো নাস্তিক,0,religion
আগে তুমি ইমান আন তার পর ভিডিও দিও,0,religion
চরম বেয়াদব,0,religion
বিপদের সময় আল্লাহর আশ্রয় চাও ‘মারইয়াম বলল আল্লাহকে ভয় করো যদি তুমি আল্লাহভীরু হও আমি তোমার থেকে দয়াময়ের আশ্রয় চাচ্ছি। সূরা মারইয়াম আয়াত ।,0,religion
এটা অপমানিত নয়,0,religion
আল্লাহ্‌ তুমি ওরে আগুনে জালাও,0,religion
তরে আমি আরকিকমু তুইত ব্দমাইশ,0,religion
মিজানুর রহমানের জন্য দোয়া ও ভালো বাসা রহিলো,0,religion
হুজুরদের নিয়ে ভিডিও করে সবাই ভাইরাল হয় রে,0,religion
পাগলের বিষয়ে কি বলার আছে?,0,religion
যারা মিজানুর রহমানকে ভন্ড বলে তারা সবাই ভন্ড,0,religion
বাঘ টাই যথেষ্ট,0,religion
এখানে ডাঃ জাকির এর দরকার ছিল।,0,religion
দেওয়ান বাগীর বিরুদ্ধে প্রতিবাদ কোরতে কেকে আছে,0,religion
বাই এই বড় বেছে আছে দেয়ান বাগি বেছে আছে,0,religion
কবরে যাও না বুঝতেপারবে তাহেরী ভন্ড তুমরা ভন্ড,0,religion
ভন্ড হুজুরে দেশ ভর্তী,0,religion
পেটুয়া দেওয়ানবাগীর এতো ভক্ত অনুরাগী ? ভাবতেও অবাক লাগে ঐ সব ভক্তদের কর্মকান্ড দেখে ছিহঃ ! ছিহঃ !,0,religion
জুত বডি মারো সালাদেরকে,0,religion
কথা গুলো খুব ভালো লাগলো ভাই,0,religion
তোদের মতো হাজার নাস্তিকের জন্য এক মামুনুল হকেই যথেষ্ট,0,religion
পাশে ছিলাম পাশে আছি ইন্শাআল্লাহ্ পাশে থাকবে আপনার জন্ন্য মহান আল্লাহ্ পাকের কাছে দোয়া করি তিনি যেন আপনার হায়াত বিদ্দি করে দেন এবং সামনের পথ চলা সহজ করে দেন যাতে করে এই রকম প্রতিবাদী ভিডিও আমরা আরে পাই আমিন অবশেষে আপনার জন্ন্য অনেক অনেক ভালবাসা ❤️💛💚❤️💛💚❤️💛💚,0,religion
জন নয় জন। উপস্থাপিকাকে বাদ দেওয়া যাবে না।,0,religion
অনেক মজা পাইছি ভাইআপনি এগিয়ে যান,0,religion
আর কিছু দিন পরে থাকবেনা,0,religion
লাহাবীর দল😂😂,0,religion
দালালি ব্যবসা বাদ দেও।,0,religion
তুই বাটপার,0,religion
বেয়াদব ছেলে বেয়াদবি শিখচজে অল্প বয়সে।,0,religion
এই রকম মাজার পূজারি কে নগত জিবনের মতো শিশিক্ষা দেওয়ার দরকার ছিল। করা করে পিটানোর দরকার ছিল। জীবনে যেমন আর প্রকাশ্যে মাজার এর নাম নিতে ভয় পায়।,0,religion
রীফুটারকে বলি আফনিবুলিকে তাকলে সংসুদন করুন আমি গালিদিলাম না,0,religion
আপনার কথা গুলি পর পুরুষে সুনা জায়েজ আছে নাকি এটা জায়েজ নিজের বোল কে দরে,0,religion
সম্মানিত ভিউওয়ার্স ভাইদের বলছি এই এডমিন ইউহুদি কৃষ্টানদের দালাল এরা ভিডিও এডিটিং করে হযরত দেওয়ানবাগী হুজুরের নামে দুষারুফ করা এই এডমিনরা এই রকম ভিডিও বানাই তাদের ভিউওয়াজ বারানু এবং মহান আল্লাহর বন্ধুদের বিরুদিতা করা আর বাস্তব দেখুন দেওয়ানবাগী হুজুর হযরত মা ফাতেমা রাঃ কে মা বলেই ঢাকেন সুধু তা নয় খাতুনে জান্নাত হযরত মা ফাতেমা রাঃ বলে ঢাকেন এবং সবাই কে ঢাকতে বলেন খাতুনে জান্নাত হযরত মা ফাতেমা রাঃ ত বৎসর পূর্বেই ওফাত হয়েছেন দেওয়ানবাগী হুজুর হযরত মা ফাতেমা রাঃ কে এখন পাবেন কই এই কথা পাগলে ও বুঝবেনা আপনারা কি বাবে বুঝেন আমার মনে হয় আপনাদের মাথায় সমস্যা আছে ভাল ডাক্তার দেখান,0,religion
হে আলেম সমাজ আপনারা সবাই কে বলছি এখন আর একে অপরকে দোষ দেয়ার সময় নেই । আাপনারা সবাই এক হতে চেষ্টা করুন।,0,religion
যারা বলছেন শিশুবক্তা কেয়ামতের আলামত তা ঠিক তবে সেতো বালেগ হয়েছে দ্বিতীয় কথা হচ্ছে সে বারিদারা মাদরাসা তথা নূর হুসাইন কাসেমী সাহেব হুজুরের মাদরাসা থেকে দাওরার সার্টিফিকেট আর্জন করেছেন অতয়েব তার বয়ান শুনা জায়েয বলে গন্ন হবে,0,religion
আপনার হাত বার বার একি স্টাইল করেন করেন কেন,0,religion
এখানে আল্লামা ওলি পুরী হক কথা বলছেন আমী নিজেই দেকেছী মসজীদে নামাজ পরতে গিয়া মেয়েরা ও মসজিদে যায় বার বার আমার নজর চলে যায় মেয়েদের দিগে সয়তান আমাদের সাতে লেগেই আছে আল্লাহ আমাদের সটিক বুজ দানকরুন আমীন,0,religion
মিজান যে বলে মাজারে যায়েজ না তা হলে বাংলাদেশে ইসলাম এনেছেন কে,0,religion
আসসালামু আলাইকুম ভাই আমি দেওয়ান বাগিকে জুতা মারার কথা বলবনা আমি বলব দেওয়ান বাগির জিবহা টা টেনে ছিরে ফেলা উচিত,0,religion
বন্ডোর শিক্ষা হয়নায়,0,religion
এই অল্প বয়সের ইচড়ে পাকা কিছু কথা মুখস্থ করে ওয়াজের নামে ব্যাবসা করছে।এই বদমায়েশ এক নাম্বার ভন্ড আর চিকন শয়তান।দুনিয়ার কি বোঝে এই নাদান বয়স্ক আর অভিজ্ঞ আলেম কি নাই অই যায়গায় যাদের কাছ থেকে কিছু শেখার আছে। এটা ইসলাম নিয়ে ব্যবসা ছাড়া কিছু না।,0,religion
বাংলাদেশর সব মেয়াদ উত্তীর্ণ মাল ভারতে যায়,0,religion
বাই তোমার কতা গুলো অনেক সুনদোর আর জিকের দেখে আমি হাসতে হাসতে মরি,0,religion
নাস্তিকদের কাছে মামুনুলহক ভাই । কেন গেছেন। এরা তিনজন নাস্তিক।,0,religion
এরা ফেরাউন এর বংসধর,0,religion
হামজা ভালো,0,religion
আসাম থেকেবছি বাংলা দেস খারাবনা কিন্তু কিছু কিছু ভনড আছে দেশ টাই খারাব করে,0,religion
ভন্ড মূর্খ অর্খোট আস্তিকগুলো নাস্তিকদের তৈরি এসব মিডিয়াগুলো ব্যাবহার করতে লজ্জা করেনা ? তোমাদের হাফেজ আলেমরা কি ছেঁড়ে ? তোমাদের জন্য ফেসবুক ইউটিউব তৈরি করতে পারেনা আল্লাকে বলে,0,religion
এক লাইক সমান তাকে জুতা তার গালে মাজার পুজারি।,0,religion
চার নাস্তিক্কে দেশ ছারা করতেহবে ওরা এদেশে তাকার কুনু ওদিকার নাই এটা মুছলমানদের দেশ কোনু নাস্তিকদের না ।,0,religion
এগুলোকে সর্বসম্নুখে ফাসি দেওয়া দরকার।,0,religion
যেকানে জাবে জোতা পিটা করতে হবে,0,religion
আজ ইসলাম কে ওরাই হাসির পাএ বানায়?কেোরান হাদিছের বয়ান কর!বদনাম কর কেন এটা কোন কওমির অাদব নয়?,0,religion
গাজা খায় আমি দেকছি,0,religion
নাস্তিকের বাচ্চা শতাংশ মুসলিম,0,religion
তুই ওয়াজ কর মানুষের দুশ বলে বেরাইশ না। য্যত্সব,0,religion
এত বড় আলেম তরার বন্ডর দলেও নাই। কথা সাবধানে বলিশ বেয়াদব,0,religion
বেয়াদব আল্লাহর রহমত হইতে বন্চিত তুমি যে একটা বেয়াদব তুমার কথায় এইটা ইসপস্ট গিয়াস উদ্দিন তাহেরি তুমার চাইতে বয়সেও বড়ো এবং এলেমের দিক দিয়েও বড়ো,0,religion
যার লজ্জা বলতে কিছুই নাই সে এই ইতর যার নাম তাহেরি নাকি তেহারি । জাহান্নামের প্রথম কাতারের লোক তাহেরি এই কথা যে পাগল সেও বিশ্বাস করবে তাহেরি নাকি তেহারি যে একজন ভন্ড।,0,religion
চর জন নাস্তিক। একজন আল্লাহ ওয়ালা,0,religion
আমি বলছি আল্লা এক আল্লা এক,0,religion
ভালো লাগলো ভাই।।,0,religion
এদের উদ্দেশ্য পরিষ্কার। ইসলাম ধর্মকে অবমাননা করাই ছিল এদের উদ্দেশ্য।,0,religion
আপনার এই পাগল ছাগলা মার্কা লোগোর জন্য আমি আন সাবস্ক্রাইব করতে বাধ্য হলাম,0,religion
মেয়াদ উত্তির্ন গাজা খাওয়ার পরিনাম,0,religion
তাহেরি তো আল্লাহ আছেন বিশ্বাস করে না তার কথাই যা বোঝাই,0,religion
হায়েরে বাংলার মানুষ তোরা এতোটা অবুজ তোরা কি ভাত খাস নাকি গাস খাচ এসব কি করে বিসাস করোস,0,religion
ইহুদিদের দালাল তোরে জুতা দিয়ে শুভেচ্ছা,0,religion
শয়তান খাজাবাবা তোরেদেখলে জুতা দিয়া পিটবো দুরহো শয়তা হেলালবাবা লোক আপসোস বেসীভাগ শিরকএ আগবর,0,religion
ফাশি চাই।,0,religion
অপমানিত না আম্মোক,0,religion
বাঙালি মুসলিমরা মুসলিম না ওরা গাঁজা খোর ইসরাইল আর ইহুদিদের চেও বড় ইহুদি,0,religion
ফরিদপুরের একজনের খোজ জানি আমার আব্বু আম্মু কে বস করসে দয়া করে কি করব বলেন,0,religion
যতটুকু বুঝলাম ভালোই লাগলো,0,religion
সাবাস ছোট ভায়েরা,0,religion
ওয়াজ করলি কই শুধু আরেক জনের বদনাম করলি।তুই বড় জালেম।,0,religion
শিশু বক্তা আবার নিজেই বলে হুজুর বাংলাদেশ আর শান্তির ধর্মের দেশ নাই তা হয়ে গেছে ক্ষমতার দেশ যার টাকা আছে সে রাজা যার টাকা নেই তার কোনো দাম নাই হায়রে দেশ কিয়ামত চলে আসছে সবাই নামাজে অনুসরণ হয় সবাই ভালো হবে কাতার থেকে,0,religion
তোরা শয়তানের বড় ভাই।,0,religion
হায়রে কত ধান্দা বাংলাদেশে !,0,religion
মিজানুর রহমানের সাথে কোন তুলুনা হয়না। মিজানুর রহমানকে নিয়ে কোন কথা হবে না।,0,religion
ধন্যবাদ ভাই অসাধারণ রোষ্ট,0,religion
এইসব ভন্ড আলেম নামের জালেম মুর্খরা সাধারণ মানুষকে ফিতনার মাঝে ফেলে দিচ্ছে।,0,religion
তাহিরিজে ভন্ড তা জাচাই কারার কি আছে সেত একটা বদমাশ,0,religion
ঘন্টা জুতা দিয়ে পিটেলে ঠিক হবে,0,religion
মাশা আল্লাহ্‌ 😍 ভাই এই ভিডিওর জন্য আমরা অনেক অপেক্ষায় ছিলাম😍 হে আল্লাহ আমাদের তাহসিন ভাইকে দ্বীনের মুজাহিদ হিসেবে কবুল কর🤲😍আমিন🤲😍,0,religion
এসব মাজার পূজারীর জন্য মুসলমানদের মদ্ধ্যে ঐক্য নাই!!!,0,religion
মুফতি সাহেব আপনি যা বলেছেন সেটা সঠিক,0,religion
জুতাপেটা করা দরকার দেওয়ানবাগীর,0,religion
লিল্লাহে তাকভীর এর অর্থ কি?,0,religion
আপনার বাবা মা এর দুর্ভাঘ তাই বোলে অন্নের সন্তান কে বিপথগামি করবেননা।নিজের সাথে জাহাননামির দল ভারি করে লাভ নেই। পরকাল ফেসবুক না যে সেখানে ফলোয়ারস থাকবে। এ যে দেখায় ও যে দেখে লেখে জনের খাতা নিয়ে নেয়।যে দেখায় তাকে খাতা দেয় কারন গেয়ানি জানেন এর যোগ্যতা। আর অন্যজনকে খাতা দিলে যা না দিলে তাই। আল্লাহ জানেন কাকে কি কখন কেন দিবেন।,0,religion
মিজানুর রহমান মহান ব্যাক্তি ওনার ওয়াজ খুব ভাল লাগে,0,religion
মিডিয়া জানোয়ারের বাচ্চা,0,religion
হাই রে বাংলা,0,religion
ভাই তুমি যদি মানুষ হও তাহলে আরেকটা ভডিও তে বলবা কারা হক্কানি,0,religion
আনলাইক দেওয়াগুলো দেওয়ান বাগীর মুরিদ মনে হচ্ছে।,0,religion
ওদের আব্বার নাম দেওয়ান বাগী😂😂😂,0,religion
ভনড জিলানী,0,religion
ভূল পৃথিবীতে আজ ভন্ডদের সংখাই কোটি কোটি। আর মুসলিমের সংখা অল্প। কারন আজান হলে যে সলাত আদায় করে সেই হলো মুসলিম গরু খাইলেই মুসলিম হয়না।,0,religion
মারা মারি না দেখে সহি হাদিসের আলোকে নিজেকে সংশোধন করার চেষ্টা করুন,0,religion
চার যনি নাস্তিক,0,religion
ওদেরকে ধইরা কুরবানী করা উচিত,0,religion
নাস্তিক ওরাই তো প্রকৃত প্রতিবন্ধী আমার ইসলাম ধর্ম নিয়া কেউ কুটক্তি করো না করলে একদম সাইজ করো দিবো,0,religion
ভন্ড দেওয়ানবাগীর ফাঁসি চাই,0,religion
আগে তর আসলাম কিন্তু জিহাদি হুজুরের ভিডিও টা দেখার পর আমি তর হেটার তুই বড় ভন্ড তর মত ভন্ডের বাংলাদেশে খুব অভাব,0,religion
মিথ্যা অপ্রচার সমালোচনাকারীদের আল্লাহ্ পছন্দ করেন না। সত্য দুর থেকে দেখা যায় না। এডমিন তুমি এটা ঠিক করো নাই,0,religion
তুমি কি হয়েছে তোমার,0,religion
এখন কোথাও মাহফিল হলে এলাকার মানুষের কাছ থেকে চাঁদা নেওয়া হয় এটা কত নম্বর হাদিস । তোমি মাহফিল করতে না পারলে কর না বালের কমিটি। নামের মুসলিম ইসলামের কোন নিয়ম পালন করে না বাংলাদেশের বেশির ভাগ মানুষ ।,0,religion
আমারা সাধারণ মুসলিম এতই অসহায় হয়ে গেছি যে এইসব নাস্তিকরা অনুস্টানে এসে প্রকাশ্যে ইসলাম নিয়ে মস্কারা করছে আর আমরা শুধু কমেন্টে এদের গালাগালি করেই সীমাবদ্ধ থাকছি।আমরা কি পারিনা এদেরকে বর্জন করতে এবং এদেরকে আইনের আওতায় আনতে আন্দোলনে নামতে??????,0,religion
মানুষের পতন আসলে পদে পদে ভুল করে বলেছেন শেখ মুজিবুর রহমান,0,religion
হুজুর ওরা নাস্তিক ওরা সত্যটা বুজবেনা,0,religion
সাব দান হয়ে জায়,0,religion
আব্বাসি সাহেব বল্ল রাস্তায় আছি আব্বাসি ওয়াজে বলেন তার প্রমান কই জেই সময় বলছে আব্বাসিকে দেখা জায় না সালা তুই খারাপ,0,religion
হায়রে নাস্তিক,0,religion
পালতু ওয়াজ। পাগল,0,religion
এই কাফিরটা প্রভাবশালী মুশরিকদের আর মূর্খ বর্বর একদল বাংলাদেশীদের ছত্রছায়ায় এই বাংলাদেশে দীর্ঘদিন ধরে টিকে আছে সরকার ও এগুলার নিরব দর্শক।শুনি শুধু এটাতে নাক গলালে ধর্মীয় দাংগা হবে আমি আজ পর্যন্ত বুঝিনি যে যারা বলে ধর্মীর দাঙ্গা হবে তারা এর মধ্যে ধর্মের দেখলো টা কি?তারা যদি এই জঘন্যতম প্রাণীটিকে ধর্মের আউতায় দেখে তাহলে তাদের ঈমান যথাযথভাবে প্রশ্নবিদ্ধ!!,0,religion
তাহেরি একটা ভন্ড তার ফাঁসি চাই ।,0,religion
এই বক্তার বাড়ি কোথায় কেউ জানলে বলবেন আমার প্রানডালা ভালবাসা রইল তার জন্য।,0,religion
ওসাদারুন।কন্ঠ,0,religion
ওহ আল্লাহ এতো ভন্ডামি কেমনে পারে দেওয়ান বাগী। 😠 ওর কোন জাহান্নামে জায়গা হবে একমাত্র আল্লাই ভালো জানে। এ সব অসৎ দের জন্য ইসলাম ধর্মের দুর্নাম হয়।😢,0,religion
ভাই ঈদের গিফট দিলেন নাকি????😁,0,religion
পিচ্চি বিচি পাকছে,0,religion
তোমার শিক্ষক তোমাকে আদব শিখায়নি,0,religion
তুই ভালো না,0,religion
ভাই সত্য কথা গুলা সবার সামনে তুলে দরার জন্য ধন্যবাদ,0,religion
বাই ভালো খারাফ আছে সবাই এক না,0,religion
আল্লা তুমি এই সব নাস্তিক দুনিয়া তে শাস্তি দাওয়,0,religion
আল্লাহ তুমি ওদের কে নিজ হাতে কঠিন তমক সাজা দেও,0,religion
এই সব ফালতু চ্যানেল তুই খারাপ কই দেখলি,0,religion
ফাসি দিতে হবে,0,religion
তোমার মাথায় কিছু নাই লোপা।তুমি আল্লাহ কে চেনো।তিনি এক তার কোন শরিক নেই। আকাশের সূর্য কে দেখ জমিনের সবকিছু দেখ।দেখে শিক্ষা নেও।আল্লাহ নিওমের বাইরে চললে কেউ রেয়াই পাবে না।একদিন এই জমিনেই আল্লাহ তোমার শিক্ষা দেবে।,0,religion
বেয়াদবের বাচ্ছা,0,religion
বেশিভাগ মাজারে তল্লাশি করলে হাজার হাজার গাঁজা পাওয়া যাবে,0,religion
নিজের সন্তানের ক্ষেত্রে ঠিকই বলছে আল্লাহ না করুক হাহাহা ভন্ড লোপা রহমান,0,religion
ওকে ভালো করে ধোলাই করা উচিত,0,religion
কাদের সাথে কথা বলতে গেছে মামুনুল হক সাহেব ওদের ভিতর তো কোনো জ্ঞানই নাই|সবগুলা নাস্তিক| যেখানে কোরআন হাদিস হবে মানুষের মডেল সেখানে ঐ নাস্তিকদের নাকি মডেল দেশ লাগবে|আল্লাহ ওদেরকে হেদায়েত দান করুন আর না হয় ধ্বংস করে দিন |,0,religion
ভাই আপনে সেইম টু সেইম হানিফ সংকেতের ছোট ভাই,0,religion
ওই তুইতো কুরআনের তাফসির করতে পারবি না তুই তো বড় বাটপার তুই ইসলামের কিছুই বুঝস না,0,religion
সাধু,0,religion
কি বলবো আর,0,religion
আল্লাহ এই সব ভন্ড দের বিচার নিজের হাতে একদিন করবেন ইনশাআল্লাহ,0,religion
ওরা কারা যারা ডিজলাইক করে!,0,religion
পুরাণ পাগলের ভাত নাই নতুন পাগলের আমদানি।,0,religion
এদের ফাঁশি চাই।,0,religion
এত পার সামনে সামনে এসে মোকাবেলা কর,0,religion
ভাই মেয়েদেরও কি এইরকম ভাবে🙄,0,religion
মোল্লা সয়তান।,0,religion
আহলে হাদিসরা হচ্চে এই সমাজের বড় ফেতনা।।এই এডমিন নিচ্চয় সে দলের,0,religion
তুই যে জিকির করছ ঐ জিকির তোর মার বোদার ভিতর ডুকাইয়া দে হারামজসদা,0,religion
তাহেরী একটা ভন্ড আল্লাহ্ হেদায়েত করুক আমিন,0,religion
ভাই আপনার কথা অনেক ভাল লাগলো।,0,religion
সত্যি কথা শুনে শয়তানের গা জলে।হুজুর সত্যি কথা বলেছেন।,0,religion
ভন্ড দেওয়ানবাগী। পেটে আর পাছায় সকাল বিকাল লাত্তি দেওয়া লাগবে। আমার তো ইচ্ছে করতেছে একটা টয়লেট টিস্যুর ফ্যাক্টরি তৈরি করে দেওয়ানবাগীর ছবি প্রত্যেক টিস্যুপেপার এ ছাপাইয়া দিবো।আর প্রতিবার হাগু করে ঐ টিস্যু ইউজ করবো।,0,religion
আরে বন্ধু তিন প্রকার চুল রাখার নিয়ম তাই তো সঠিকভাবে তুই জানোস না এক প্রকার কানের লতি পর্যন্ত দুই প্রকার একদম ছোট ছোট করে তিন প্রকার একদম মাথা ন্যাড়া করে তোদের মত বন্ধুদের কাছ থেকে সাধারণ মানুষ কি শিখবে,0,religion
যাদের সামনে এই কথা গুলো বলছে তারা এই ভন্ড কাফেরকে জুতা দিয়ে মূখে আঘাত করে না কেন ।যেন তার মুখ দিয়ে কোনো শব্দ উচ্চারিত না হয় ।এই কাফেরের কথা শোনার ধৈর্য আমার নাই।,0,religion
হাফিজুর রহমান হল একটা ভন্ড কুকুর,0,religion
টাকা ভাই টাকা,0,religion
এরা হচ্ছে ইসলামের শত্রু,0,religion
হুজুর আপনাকে আমার অনেক ভালো লাগে নাস্তিক দের লাথি মারতে মনেচায়,0,religion
জনগণের প্রতিবাদ দেখে মনটা ভরে গেলো হক্কানি আলেমের হক কথা শুনে মনটা ভরে গেলো আল্লাহ এই হুজুরকে নেক হায়াত দান করুন এবং প্রতিবাদি মানুষদের।।,0,religion
কারে সাথে কার জোরা দেয় ।কোথায় তাহেরি আর কোথায় আজহারী। আজহারীর মত হক দার বক্তা আমি কখনো দেখি নাই,0,religion
আমি মাজারগুলিতে থুথু দি আর ভন্ডদেরকে মাইর দিই।,0,religion
লাথি মারেন মেরে যান। ভন্ড মাজারপূজারী,0,religion
মিজান হুজুর ঠিক বলচে,0,religion
দুঃখিত ভাই পুরা ভিডিওটা দেখতে পারলাম না কারণ এই ভন্ড কথা শুনলে আমার মেজাজ অনেক গরম হয়ে যায়,0,religion
আল্লাহ র গজব পড়ুক এদের মতো নাসতিক দের উপরে জাহান্নাম তো আল্লাহ তোদের দিবে আর আল্লাহ তোদের মত নাস্তিক দের ফল দুনিয়া থেকে দেখাইয়া নিবে ইনশা আল্লাহ,0,religion
খুলে যাক চোখ বন্ধ হোক গোঁড়ামি।। আপনার কথায় মত,0,religion
শালা ভন্ডো,0,religion
আপ্নি যে হাদিস বল্লেন তার সাথে চুলের কোন সম্পর্ক নাই,0,religion
এটা জিকির না এটা বাবুল গানের নাচা নাচি আল্লা আমাদের সকলের সঠিক বুঝ বোঝার তোউফিক দান করুন আমিন,0,religion
ভাই পুরাটা দেখলাম না ওই সালার কথা শুনলেও পাপ হবে। শুধু এটা বলবো আল্লাহ গন্ডার টার হেদায়াত করুক।,0,religion
তরে পাইলে মাইরা ফালাইতাম,0,religion
হা হা হা বিনোদনে ভরপুর।,0,religion
যারা তাহেরী হুজুরে গালি দেন তাদের উপর গজব পরুক।,0,religion
আল্লাগো আল্লাহ আমাদের মাফ কর। এ কেমন দেশে আছি। আল্লাহ তাদের বিচার এ জমিনেই দেখিয়ে যেইয়ো। মানুষ গুলো যাতে শিক্ষা পাই,0,religion
ধর্মে ভন্ডামি আসতে আসতে উন্মোচন হচ্ছে বুঝা যাচ্ছে ধর্মে যে কিছু নেই শুধু হিংসা সমালোচনা ছাড়া,0,religion
একে কিছু করা উছিত ওকে খুন করলে কি পাপ হবে জানতে চাই একটু,0,religion
ডাঃ নায়েক সত্য তুলে দরার জন্য ধন্যবাদ,0,religion
এদের কপালে জুতার ভারি তারা আবু জাহেল মার্কা লোক,0,religion
আজহারি চরম বেয়াদব,0,religion
আমার প্রিয় বক্তা মিজানুর রহমান আল আজহারি,0,religion
ভাই মনডায় চায় ওদেরকে কুত্তা দিয়া খাওয়াই। আল্লাহ এগুলার উপর গজব ফালায় না কেন???,0,religion
এই হুজুর ঠিক বলেছেন,0,religion
ভাই এত ছোট ভিডিও আপনি এত বড় করার দরকার টা কি???,0,religion
আসসালামু আলাইকুম ভাই। দেওয়ান বাগী যে ভন্ড এতে কোনো সন্দেহ নেই। কিন্তু ভাই আল্লাহর আকার আছে। নিরাকার নন।আপনি দয়া করে একটু ভালো ভাবে জানার চেষ্টা করেন। আমি রেফারেন্স দিতে পারবো। ইনশাআল্লাহ।,0,religion
ভারতে আয়,0,religion
সয়তান আব্বাছি,0,religion
যাহারা এই বাচ্চা পোলা পানের ভিডিও দেখে আত্মহারা হচ্ছেন। তারা বোকার স্বর্গে আছেন। দেওয়ানবাগী কোন কাজ ইসলাম বিরোধী করছে না। আপনারা ফালতু পোলাপানের ভিডিও দেখে নিজের ঈমান নষ্ট করবেন না। সুরা বাকারার নং আয়াতে যে কথা বলা হয়েছে যে আল্লাহ বনী ইসরাইলের নিকট তাবুক নামক একটি সিন্দুক পাঠিয়েছে। সেই সিন্দুকের মধ্যে সকল নবী রাসুলের ছবি মোবারক ছিল। যাহা ছিল খুবই বরকত ময়। । ঐ খানে বিস্তারিত নাই। তাই আপনারা বুঝতে পারছেন না। আগে জানুন তারপর মানুন। ছোকড়া পোলাপানের কথায় শুধু হু হু করিয়েন না। দেওয়ানবাগী আল্লাহ পাকের জাত পাকের উপর খন্ড তাফসীর লিখেছেন। এছাড়া কোরআনের আলোকে সম্পূর্ন জীবন বিধান রচনা করছেন। তিনি ইসলাম ধর্মের অসংখ্য সংস্কার করেছেন। তার সন্তান সহ জামাই ও নাতিরা ইসলামের উপর পিএইচডি ডিগ্রী অর্জন করিয়াছেন। তারা কোন কর্ম ইসলামের বিরুদ্ধে করিতে পারে না। যারা তার বিরুদ্ধে অপপ্রচার করে ধর্মের ক্ষুদ্র জ্ঞান দিয়ে তার বিরুদ্ধে মিথ্যা ভানোয়াট কথা বলিয়া সাধারণ মানুষকে ধোকা দেয়। তারা ইউটিউব চ্যানেল ব্যাবসার কাজে লাগিয়ে অর্থ আয় করছে। তার ব্যাপারে না জানিয়া হুজুগে নাচিয়েন না। কোন ব্যক্তির বিরুদ্ধে মন্তব্য করতে হলে নিম্নে দিন তার নিকট অতিবাহিত করতে হয়। আপনারা না জানিয়া তার বিরুদ্ধে বাজে মন্তব্য করছেন। ইহা ঠিক নয়। একমাত্র দেওয়ানবাগী হুজুর রাসুলের সঠিক ধর্মকে জগতের মাজে তুলে ধরছেন। আপনারা তার কাছে গেলে বুঝতে পারবেন। ধন্যবাদ সকলকে।,0,religion
ওরে আমার কাছে একটু পাঠিয়ে দেয়। এই বয়সে ওকে ওয়াজ করতে দেয় কেন? ওর খতনা হইছে তো?,0,religion
তুই শালা,0,religion
বাংলাদেশ এ সবাই বাবা আর গান গাই । এমন কি যে বলে যে মাওলানা গান গাই ও নকল করে দেখায় । বাংলাদেশ এ সবাই গান গাই,0,religion
আহ্ বলদ,0,religion
এদের কে ফাঁসি দেওয়া উচিত,0,religion
কবরের ভিতরে যত আজাব আছে নাস্তিক গো দুয়ার উচিত ওরা জানি কখনো মাফ না পায় আল্লাহ তাআলা এমন জানি শাস্তি দেয় তাদের দুনিয়ার মধ্যে জানে দেখা দেয়,0,religion
এরা নাস্তিক ওদেরকে আল্লাহ সহি দিন বুজার তফিক দান করুণ আমিন,0,religion
তুই যে নাস্তিক তুই এভাবে প্রমাণ দিলি,0,religion
তাহেরী আপনার ভয় নায়। আপনে চালায়া জান।,0,religion
যত সব ভন্ড বাংলাদেশ ভণ্ড চিটিংবাজ বাংলাদেশ ভরে গেছে আমাদের পশ্চিমবাংলা টাকে বাংলাদেশের হিন্দুরা খারাপ দিকে নিয়ে যাচ্ছে,0,religion
ওরা যদি ভন্ড হয় তাহলে জাকির নায়েক মতিউর রাহমান মাদানী এরা আরো বড় ভন্ড।,0,religion
ওরে প্রতিটা মন্চে জুতা মারার দরকার।,0,religion
তাহেরি হারামি,0,religion
মিজানুর রহমান হাজারী সেতো একটা কিরিস্টান তুই কি পাগল নাকি,0,religion
? এই খেলা ত আমি ছুডো থাকতে খেলছি😃😃😃,0,religion
মুসলিম বলে আগে কোনো ধর্ম ছিলনা,0,religion
তাহেরির জুতা মুছার যোগ্যতা নাই বেটা তোর,0,religion
এই ভন্টকর আইনের আওতায় আনা দরকার,0,religion
এডমেন তোমার বাবা কে কি দুলা ভাই ডাকু না কি হা হা হা,0,religion
হুজুরদের অবস্থা এখন এই একজনের পাছার ভিতরে আয়জনের আঙ্গুল দেওয়া,0,religion
তদের মত কিছু কিছু ইউটিউবকে সারভার টিমে অবিযোগ করা দরকার,0,religion
আল্লাহ ভন্ড তাহেরীকে হেদায়ত করোন আমিন সারা বাংলাদেশকে নস্ট করে দিছে,0,religion
যদিও শিশুদের ওয়াজ শুনা ঠিক না তবুও শুকরিয়া আদায় করি এই ছেলেটা যে বয়সে গান বাজনা নিয়ে ব্যস্ত থাকতো সে বয়সে সে আল্লাহর পথে দাওয়াত দিতেছে।,0,religion
অভদ্র মুরিদ🙂,0,religion
শাহরিয়ার কবিরের মত দুই একটা নাস্তিক গুলি করে মারলেই বাংলাদেশের মুসলমানরা শান্তিতে থাকতে পারবে। আর আমি মনে করি এরকম নাস্তিকদের কে গনদোলাই দিয়ে মেরে ফেলা উচিত।,0,religion
আমির হামজা একটা ফাজিল তাহেরির কাছে বার বার খমা চায়,0,religion
চা খাবেন? ঢেলে দেই? ভন্ড মাজার ফুজারির দল।,0,religion
আল্লাহ পাক আমাদের সবাইকে রাসূল সাল্লাল্লাহু আলাইহি ওয়াসাল্লামের আদর্শ অনুযায়ে চলার সৌভাগ্য দেখ আমিন 😭🥰,0,religion
এদের বিচার হয়না কেনো,0,religion
এই চার নাস্তিক কে জুতাপেটা করে বের করে দেয়া হোক বাংলার জমিন থেকে কে কে একমত লাইক দাও👇👇👇,0,religion
আমাদের দেশে কোন বিচার আইন নেইতো যার যা মন চাই তাই করেন,0,religion
পাগলে কি না বলে ছাগলে কি না খায়।,0,religion
সাল্লা তুই কি জানস,0,religion
মানুষ নাকি,0,religion
জন যদি নাস্তিক হয় সেখানে কিছু বলার নাই,0,religion
হে দালাল তুই কি লিকচিস লেখাটা পালটা তর কি আল্লাহ ভয় নাই কারে কি বলিস।,0,religion
এসব মানুষ মবিলে আসে কেন মুসলিম নামের জানোয়ার হুজুরের কথা টক্কর ধরে ও একটা গাঁজাখোর মতন বসে থাক,0,religion
এসব কাফেরদের বিরুদ্ধে সরকার কনো ব্যাবস্থা নেয়না কেনো,0,religion
না না এবং না,0,religion
ভালো কাজ করেছেন ভাই।মসলা ভালই ছিলো,0,religion
তাহেরী হুজুর মারহাবা,0,religion
শিশু বক্তার উদ্দেশ্য বলছি । বাইয়া তুমি ছোটো গিয়াসউদ্দিন আল তাহেরি তোমার বয়সে বড়।আর বড় দের শম্মান করতে শিখো ওকে,0,religion
হগ হ কিন্তু আমির হামজাকে মানব না অ কোনো মসুলমান না,0,religion
আমাদের আল্লাহ রাব্বুল আলামীন বলেছেনঃ যে কিয়ামতের কিছু আলামত পাওয়া যাবে কেয়ামত হবার আমার বলা ঠিক হবে না কিন্তু এটাই কি তার আলামত,0,religion
রাইট বার এইশালা আসলে বাট পার ওর কতা না বলাই ভালো,0,religion
ভাই ওদের জুতা মারেন,0,religion
সত্যি এই লোকগুলিকে কি যে করতে ইচ্ছে করছে।।আল্লাহ কিভাবে সহ্য করছে জানিনা,0,religion
অামি যদি একবার পাইতাম ওরে জুতার বাড়ি দিতে দিতে মাইরা লাইতাম।,0,religion
ছোট দেরকে দিয়ে যেসব কতা যারা বলিয়েচেন তারা হলেন ইসলামের দালাল,0,religion
ভাই আপনি মনে হয় জানেন যে মিজানুর রহমানই আযহারিই একমাত্র ব্যক্তি যিনি আযহারি বিশ্ববিদ্যালয় থেকে পড়ে আসছে বলে এবং সাথে বক্তব্যের সময় কিছু কিছু ইংলিশ বলে বলেই তাকে আপনি তথা আপনাদের মতো কিছু মানুষ তাকে মনেকরে থাকেন।আসলে কি ভাই আপনারা যাকে সমর্থন দিয়ে যাচ্ছেন তারাই আপনার ইমান ধংস করে দিচ্ছে জানি এখন বুঝবেন না বুঝবেন সময় হলে যখন উপায় ও সময় থাকবেনা ।আরে ভাই মিজানুর রহমানের মতো আরো অনেকেই আছে যারা আযহারি বিশ্ববিদ্যালয় থেকে পড়ে এসেছে যাদের সাথে ওনার কোনো মত মেলে না।সে একাই নিজে থেকে বানিয়ে বানিয়ে নিজের ইচ্ছায় কথা বলে যা কোর আন হাদিসের সাথে মেলে না।আরে ভাই আল্লার রাসূল সাঃ বলেছেন অন্য নবীদের উম্মত গ্ণ কাতার হয়েছে আর আমার উম্মতের মধ্যে কাতার হবে টি তখন সাহাবি রাঃ গণ জিজ্ঞাস করলেন কোন দল জান্নাতে যাবে তার পরিচয় দিন অন্য গুলোর দরকার নেই তখন রাসূল সাঃ বললেন যাদের সাথে আমি ও আমার সাহাবিদের সাথে মিল থাকবে তারাই জান্নাতি দল।আল্লার রাসূল সাঃ বিদায় হজ্বের ভাষণ দিতে বলেছে তোমাদের জন্য দুটি জিনিষ রেখে যাচ্ছি তা ধরে রাখলে তোমরা কখনো পথভ্রষ্ট হবে আল্লাহর কোর আন আমার হাদিস ।এই হাদিস সম্পর্কে তখনকার সকল তাবে তাবেঈ গ্ণ বলেছেন হাদিস বলতে হুজুর সাঃ এর বংসধরদেরকে বুঝিয়েছেন।আর আল্লাহ্‌ তা য়ালা বলেছেন হে হাবিব সাঃ আপনার বংসধরকে কিয়ামত পর্যন্ত আমি পবিত্র রাখবো।আর আপনি এনায়েতুল্লাহ আব্বাসি হুজুরের গিবত করলেন সেও একজন রাসূল সাঃ এর বংসধর আব্বাসি বংস আর ভাই ভুলে গেলে চলবেনা আমাদের ভারত উপ মহাদেশে যারা ইসলাম এনেছে তারা আল্লাহর ওলি তাদের বাদদিলে আপনারা আমরা মুসলমান থাকবোনা।আপনার মিজানের সাথে আল্লাহর কোনো হক্কানি ওলি আউলিয়াদের মত মিলেনা আল্লাহ্‌ বলেছেন তোমরা সাবধান হয়ে যাও আমার ওলিদের ব্যপারে কারণ তারা আমার কাছে চলে এসেছে তারা যা দেখে তা আমার কুদরতি চোখ দিয়ে দেখে তারা যা ধরে আমার কুদরতি হাত দ্বারা ধরে সুতরাং যারা আমার ওলিদের বিরোধীতা করবে তাদের বিরূদ্ধে আমি যুদ্ধ ঘোষণা করবো ।আপনি ভাববেন এতো বড় কামেন্ট !হ্যা জানিনা আল্লাহ্‌ আপনার কপালে হেদায়েত রেখেছে কিনা জানি না যদি থাকে তাইলে আপানার এ কিছু কথা আপনা আপনি ভাববেন।আর নিজেকে বানানোর জন্য গিবত কে বেছে নিয়েছেন ভাই দুনিয়াটাতে এই আছি আর এই নেই তাই মানুষের গিবত না গেয়ে জীবণকে সুন্দর করুণ।,0,religion
আাললা তুমি এই নাস্তিক দের ধবংস কর আমিন,0,religion
বাংলাদেশ কি করছে দেখছেনা এদের,0,religion
সুন্নিরা কখনো ওহাবীদের সামনে ভয় পাইন হোক তারা লক্ষ যেমটি এই ভিডিও তে দেখলাম,0,religion
নাউজুবিল্লাহ এই ভন্ড দেওয়ানবাগীর ফেরাউন এর চেয়ে খারাপ তাকে আগুনে পুড়ে মারা হোক,0,religion
কবিরের চেতনার গুসটি চুদি,0,religion
ওই বেয়াদব কুতি,0,religion
গাধাগুলো মামুনুল হকের কথা বলতে দিচ্ছেনা কি বলছে ওরা! শয়তানরা বুঝতেই পারছেনা মামুনুল হক কি বলছে ? পাগল ছাগল সব,0,religion
বেয়াদব বাটপার 😡😡😡,0,religion
কবর পূজারিরা কবরের মাজারের ও রওজার বিরুদ্ধে কথা শুনলে ওদের শরীরে আগুন লেগে যায় । কারন ওরাই হলো আসল শয়তানের বড়ো পান্ডা ॥,0,religion
রাসুল অর্থ রেসালাত দান কারী আল্লাহ্ পাক যাদেরকে রেসালাত দান করেছেন যাদের কাছে বিধান এসেছে। অলি আল্লাহ্ অর্থ আল্লাহ্ র বন্ধু বেলায়েতের যুগে যারা ধর্ম প্রচারের কাজ করবেন তাদেরকেই অলি আল্লাহ্ বলেন । অলি আল্লাহ্ র শান মান মর্যাদা অনেক বেশি । সূফি সম্রাট হযরত শাহ্ দেওয়ানবাগী মাঃআঃ,0,religion
ভাই তুমি কোরআনের কতটুক জানো যে তুমি বুঝে গেলে যে এই শিশু বক্তাই সঠিক আর বাদ বাকি খারাপ যাকে যাকে খারাপ বোলতেছে অই ?,0,religion
কিছু মানুষের দেমাগ বিগড়ে যায় তাই তারা আজহা রী কে খারাপ বলে,0,religion
তাকে জুতার বারি দেওয়া উচিত,0,religion
এদের কেন ওয়াজ করার জন্য সার্টিফিকেট দিছে,0,religion
ভাইয়া এ সব বন্ড হুজুর দের ব্রাশ ফায়ার করে মেরে ফেলা ভাইয়া আমার একটা হিস্ট্রি আচে আপনারা যদি আমাকে ইউটুবের মাদ্দমে সাহায্য করেন খুব উপকার হয়তো প্লিজ,0,religion
সে তো নারী নাকি জাহান্নামী আল্লাহ ভালো জানেন বেয়াদব মহিলা মাথার চুল কি করে বসে আছেন,0,religion
আল্লাহ্‌ ওনাদের কঠিন শাস্তি দিন।,0,religion
এই নাস্তিক গুলোকে ঈমান দান করুন হেআল্লাহ,0,religion
কেমন আছো বড় ভাই,0,religion
নাস্তিক েএরা চোর এরা ইসলাম বোঝে না,0,religion
মাশ আল্লাহ,0,religion
ভাই পক্কে আছি যারা ভন্ডদের পক্ক হয়ে কথা বলে তাদের আল্লাহ। জাহান্নাম নচিব করোক,0,religion
ররররন,0,religion
দেওয়ান বাকি সয়তান,0,religion
মিজানুর রহমান আজহারী সেরা,0,religion
এই বেদোবির বিচাই বন্দুরা আমি কি ঠিক কথা বলেছি,0,religion
ভাই উনাকে নিয়ে কেনো বিডিও করেন উনি মাজার পূজারী ভন্ড সবাই জানে উনার প্রত্যেকটা ওয়াজের মধ্যে ভন্ডামি আছে কোরআনের আলোচনা ভন্ডামি করে চলে না,0,religion
ভিডিও টা এডিড করে ভালো করে লেখ তা নাহলে তোর কপালে দুঃখ আছে বলে দিলাম এই চ্যানেল কে,0,religion
আল্লাহ্‌র আকার আছে।এতে কোন সন্দেহ নেই।তবে আল্লাহ্‌ আকার তার নিজের মতো।আল্লাহ্‌র আকার কি রকম এটা কোন মানুষ বলতে পারবে না। যদি বিশ্বাস না হয় নিযেই জাচাই করে দেখুন।ক্বুরান এর এই আয়াত গুলি সাথে তাফসীর ও ব্যাখা গুলি। আল্লাহ্‌র আকার নেই যদি কেউ বলেন তাহলে নাস্তিক দের মতের সাথে আপনার মিল আর অমিল কোথায়?,0,religion
আইনের সহযোগিতা অত্যন্ত গুরুত্বপূর্ণ হে আল্লাহ তুমি পথ দেখাও আমিন।,0,religion
হুদার শাক্কি তরে পাইলে জবাইকরতাম,0,religion
হুজুরের কাছে প্রশ্নঃ গীবত গাওয়া কি?? যারা অন্য করে তাদের কে হেদায়াতের জন্য দোয়া করবেন। এতো সুন্দর পরিবেশ নষ্ট করে দিলেন আপনি।,0,religion
হে বেয়াদবের ঘরের বেয়াদব,0,religion
জন ডিসলাইকা কারীরা কারা! ভন্ডবাবার অনুগত অনুসারী মনে হয়।,0,religion
এরা যে কয় জন ইসলাম এর পিছনে লেগে আছে এদের ইসলাম এর পেছনে লাগার একটাই কারণ একটাই উদ্দেশ্য এরা নিজেদেরকে হাইলাইট এবং পপুলার করতে চায় তা ছাড়া অন্য কোনো কারণ নেই আর এদেরকে নিয়ে এত মাতামাতি করার কোনো দরকার নেই আমাদের। এরা এমনিতেই নাস্তিক ছিল আছে এবং তওবা না করা পর্যন্ত থাকবে,0,religion
দুনোটা আলেম আমরা কার কতাসটিক মেনে নেব আমরা,0,religion
ইসলামকে না জেনে এরা ওয়াজ করে।,0,religion
আহাজারী দেশ থেকে পলাতক কেন?,0,religion
তুরে জরম ঠিক না,0,religion
ইনতো মুখ মাফি,0,religion
তোদের গালে জুতা মারা উচিত 🇧🇩🇧🇩😬😬😤😤👣👹👹জানো আরের দোল,0,religion
পাকা শয়তান,0,religion
এদের ফাঁসি ছাই,0,religion
হাফিজুর রহমান মূর্খদের সরদার,0,religion
এই নাস্তিকদের কেন আল্লাহ তায়ালা শাস্তি দেননা দেখলে কলিজা ফেটেজায়🐓🐓🐓🐓🐓🐓🐓🐓🐓🐓🐓🐓🐓🐓🐓🐓🐓🐓🐓🐓🐔🐔🐔🐔🐓🐓🐓🐔🐔,0,religion
নাস্তিক এর উপর জন আল্লাহর মোমিন ভারি পরবে ইনশাহ আল্লাহ,0,religion
আববাসী শয়তান ওরে জুতার বারি,0,religion
আপনি তো এক প্লেটে দেখছি ভাত ও খাচ্ছেন আবার পায়খানাও খাচ্ছেন। পাগলে কি না কয়,0,religion
আব্বাসি গাব গাছির বাচ্চারে একটু ধরেন,0,religion
তোমারে কি ফুটকি মারছে,0,religion
সালা ভোডো তাইরি,0,religion
তুর ওপর আল্লাহ্ গজব পরুক,0,religion
তাহেরীর সাথে কি আপনি চার রাত সুয়ে ছিলেন সত্য কি না জানাবেন,0,religion
তেরে মেরে ডান্ডা এবার বন্ড তাহেরী হবে টানন্ডা,0,religion
আমির হামজা কে ধন্যবাদ,0,religion
এটার জন্য অপেক্ষা ছিলাম।।অনেক ধন্যবাদ ভাই।।,0,religion
নাকে টিপ দিলে দুধ বেরহবে ঢাকা মতিজিলে জান মানুস কে বিভরানতি করসিস,0,religion
আমরা বিবভ্রান্ত হই না হুজুর।ঐ বন্ডরা হয়।,0,religion
সালারে পাইলে জোতা দিয়া বাইরামু।।।ভাইয়েরা এগিয়ে যান।।।,0,religion
অসাধারণ ভাই। আমার দুয়া রইল আপনার প্রথি।,0,religion
আপনার সাহসের প্রশংসা করতে হয়।,0,religion
এই আল্লাহ এই নাস্তিকে টি হেদায়ত কর,0,religion
মোলানা কিতাওছে,0,religion
এ,0,religion
ভন্ডামির দল,0,religion
কিসের ভিডিও দেইখাম নাউজুবিল্লাহ বলতে বলতে কুল পাইনা😠😠😠😠,0,religion
লাইক বেশি পেতে আলেমদের নামে মিথ্যাচার করছো সাবধান নিজের বিপদ নিজে ডেকে এনো না গাধারাম,0,religion
কোরআন শরীফে জুতা রাখছে,0,religion
চার কুকুর ঘ্যাও ঘ্যাও করে,0,religion
যারে প্রশ্ন করছে সে একটা নাস্তিক আর সবাই ভন্ড,0,religion
বাতিল লক্ষ জনের বিরুদ্ধে একজন হক ই যথেষ্ট। আর আল্লামা মামুনুল হকের সাথে হাজার নাস্তিক আসলেও যুক্তি তর্কে কখন ই তাকে পরাস্ত করতে পারবে না ইনশা আল্লাহ,0,religion
ঐই লাল জাওলা একটা জানওরে বাছা,0,religion
আল্লাহ মৃত্যু প্রযন্ত যেন তোমার গোলামী করে যেতে পারি। আর এদের হেদায়েত করো।,0,religion
ধন্যবাদ ভাই এরকম একটা ভিডিও বানানোর জন্য,0,religion
ইসলামের প্রবিত্র গ্রন্থ কোরানের প্রকৃত মূল্যায়ন করা মহান মানুষ গোলোর মধ্যে মুফতি মাসুদো একজন। এটাকেই বলে আল্লার সৃষ্ট কোরান শরীফ।,0,religion
আল্লাহ তোকে যিবনেও মাপ করবেনা,0,religion
মাহফিল তুমি পারে ও আহারে,0,religion
নাস্তিক এর বাচ্ছারা নাস্তিক পানা করে কোন বঙ্গবন্ধুর কথা যে বলছে? মুসলমান হলে ইসলামের পথ অনুসরণ করতে হবে,0,religion
মাওলানা আমির হামজাকে আল্লাহ্ তালা হায়াদ দারাজ করুক। আমির হামজা বেদাতের বিরুদ্দে কথা বলে তাই অনেকের গায়ে আগুন জলে,0,religion
ভাই দেওয়ানবাগী অবশ্যই হিরুয়েন খেয়ে বক্তব্য দিয়ে থাকেন এটা প্রমাণিত 😊😊,0,religion
ভাই তাকে কেউ খারাপ বলবেন না কারণ বাপের সমান লোক ব্যায়াধবী করলে এটা বললে কি ব্যায়াধব আপনারা বড় হয়ে ব্যায়াধবী করেন আপনাদে এটা আমরা প্রত্যাশা করি সে যা বলছে সে তো ভুল বলে নাই কুরান কোন হাসির পাত্র না কেউ এটা হাসির পাত্র মানে,0,religion
ভাইরে ভাই মিনিটের ভরা। ভাভাগো ভাভা।,0,religion
আবাল মার্কা বক্তা,0,religion
এই ধরনের নাস্তিক দের টিভি চ্যানেলে ডাকে কারা।,0,religion
বাল পাকনা এগুলা আসে কোথা থেকে,0,religion
নাস্তিক টা,0,religion
এই গুলা জারা করে তারা কুকুরের চেয়ে খারাপ।কারন আমরা মুসলমান,0,religion
আমার মতো যারা ডাঃ মিজানুর রহমান আজহারী হুজুর কে ভালো বাসেন তারাই লাইক দেন💖❤,0,religion
আল্লাহ ওদেরকে কখনোই ক্ষমা করবেন না জাহান্নাম আমি দোয়া করি,0,religion
তুমি তো আলেম না আমি বলবো তুমি একটা জালেম।কারন জিকির নিয়ে কটুক্তি করার অধিকার তোমাকে কে দিলো।তা ছাড়া পরের সমলাচনা করা কোনো আলেমের কাজ নয়।তোমার উচিত ছিলো যে এই কাজ করেছে তাকে সামনাসামনি বুঝানো। তুমি তা না করে পিছনে গিবদ করছো। আর গিবদ করা জিনার সমতুল্য। আর যেই লোকটা বাধা দিলো তার ঈমানের জোর আছে বলতে হবে ওই খানে একটাই বাঘের বাচ্চা।,0,religion
জুতা দিয়া মারতে ইচ্ছা করতাছে নাস্তিক দেরকে,0,religion
দুনিয়ার বুকে যেন দেওয়ান বাগির বিচার হয় যেন টাডা পরে আললা তুমার গজব নাজিল করে দাও,0,religion
মুসলিম ধর্মে কোন হাদিসে বলা হয়নাই যে গান বাজনা কর | এই গোলা সব হারাম জাদা এদের কে জুতাদিয়া মারা হোক,0,religion
নাউযুবিল্লাহ্ বইলাই কুল পাইলাম না 🙄 ভিডিও দেখবো কোন সময় 🤔🙄,0,religion
সালা তুই মাজার পুজারি ভন্ড তোরে কে আনচে,0,religion
তুই কি নাটক করছ কেন ।লাল কাপড় লাগাছ কেন লাল কাপড় ত উরুনা হয়,0,religion
হঠাৎ মানুষ গুলোর মাথা নষ্ট হয়ে গেলো নাকি এদের মাথা নষ্ট তাই কষ্ট করে এতো কিছু করছে। এত কষ্ট করার দরকার কি আপনি যদি বিদ্রোহ করিতে চান তাহলে দেওয়ানবাগীকে জিজ্ঞেশ করুন আপনি যদি সত্য জানতে চান তাহলে ও দেওয়ানবাগীকে জিজ্ঞেশ করুন। পেছন থেকে কেন উনার বিরুদ্ধে ভিডিও এডিথ করে মিথ্যে প্রচার করছেন। এর আগে ও আপনারা বলেছেন দেওয়ানবাগী মারা গেছে কই উনি তো মারা যান নি উনি তো এখনো প্রতি শুক্রবার মতিঝিল আরামবাগে বাবে রহমতে বসে বাণী রাখছেন। আপনারা ভাবছেন মিথ্যে প্রচার করে সমাজে বিভ্রান্তি সৃষ্টি করবেন সমাজ এখন আর বোকা নয় আপনাদের মিথ্যে প্রচারে সায় দিবে না মনে রাখবেন একদিন এই সমাজ ই আপনাকে মিথ্যে প্রমানিত করবে।,0,religion
জাযাকাল্লাহ খায়ের চালিয়ে যান ভাই জয় হবে একদিন ইনশাআল্লাহ,0,religion
তুই কি ওয়াজ করলে এখানে শিকার মত কিছুই পাইলাম না শুধু সাফাই গাওয়া আর বদনাম গাওয়া ছাড়া বিঃদ্রঃ আমি কোন তাহেরী আব্বাসি ভক্ত না।,0,religion
দেওয়ানবাগী কে জুতা মারা ও ফাসি দাবী,0,religion
মন গড়া ওয়াজ,0,religion
মাল কামানি শুরু করছত বদনাম বাদ দিয়া ওয়াজ কর,0,religion
আরে ভাই উনি কিসের হুজুর ভন্ড।।,0,religion
ভাইয়া ধ্যনবাদ আপনাদের কিন্তু ইসলামী সত্যি কারের পথে যারা তাদের নিয়ে কিছু বানিয়ে না এদের মতো ভন্ডের নিয়ে বানাও,0,religion
তর বাপ,0,religion
শাহারিয়া তোর যে কি অবস্থা হবে আল্লাহই ভালো জানে,0,religion
সুন্দর গলা,0,religion
তুই আরো বড় বন্ড।যে আরেকজনের বদনাম বলে বেড়ায়। আল্লাহ তাকে কোনোদিন খমা করবেন না।আমরা জানি যে দেওয়ান বাগি বন্ড। কিন্তু কাউকে অপমান করা আল্লাহ পছন্দ করেন না। তুমি তোমার পরকালের চিন্তা করো। দেখবে জীবনে কতো গুনা করেছল।তখন আর অন্যর সমালোচনা করার সময় পাবেনা।,0,religion
আল্লাহ ওদের কে এ পৃথিবী কঠিন শাস্তি দিয়ে দুনিয়া থেকে নিপাত করেন।,0,religion
আমিৰহামজা মোনাফেক,0,religion
মাওলানা হাফিজুর রহমান সিদ্দিকী কি ভাবে ভন্ড পীর হলেন,0,religion
মুসলিম ঘড়ে জন্ম নিলে সবাই মুসলমান হয় না,0,religion
হিজবুত তাওহীদ রাজি থাকলে লাইকদিন,0,religion
আল্লাহ ওদের হেদায়েত করো,0,religion
মাশা আল্লাহ হকের পক্ষে মানুষের ঈমানি হুংকার দেখে মনটা ভরে গেল।,0,religion
আরে তোমরা মানুষের নামে গীবত গাও কেনো।তোমাকে এইখানে গীবত গাওয়ার আনে নাই বুজলা।আগে নিজেকে ঠিক করো তারপর মানুষকে সঠিক পথ দেখাও।,0,religion
তাহেরীর বাচ্চা,0,religion
এই বক্তারে জুতা দিয়ে পিঠিয়ে স্টীজ থেকে নামিয়ে দেওয়ার দরকার।এই ধরনের বক্তারাই যত জামেলার মূল।,0,religion
ওরা সবাই ভন্ড,0,religion
হা হা হা মজা পাইলাম,0,religion
হুজুর বালোহয়েজা পালথু কথা লাখ,0,religion
আমি এই ভিডিওর বেশির ভাগ কমেন্ট দেখলাম যে সবাই পিচ্চি পোলা হুজুরের বিরুদ্ধে।,0,religion
যারা ডিসলাইক করছে তারা মনে হয় দেওয়ানবাগীর মুরীদ😂😂😂,0,religion
নিজেকে খুব অসহায় মনে হয় কারন মুসলিম হয়ে আমরা এদের কিচু করতে পারছিনা আল্লাহ্‌ এদের বিচার কর,0,religion
ঐ মিয়া বুইজ্জা কথা বইলেন না বুইজ্জা নয়,0,religion
মককা মদিনা কে মডেল মানব কেন যদি না তারা কোরআন হাদিস ফলো না করে?নবী রাসুলদের ফলো করতে হবে।,0,religion
বন্ধুরা ইউটিউবে আমি নতুন আমার চ্যানেলটি সাবস্ক্রাইব করে ইসলাম প্রচার করতে সহযোগিতা করুন আপনাকে সহযোগিতা করবো ইনশাআল্লাহ,0,religion
আল্লাহ পাক হেদায়েত করুন,0,religion
একটু কম সময়ে শেষ করতে পারলে ভালো হয়,0,religion
বন্ড।।,0,religion
নামাজে হুজুরীঃ সূফী সম্রাট হুজুর ক্বেবলাজান মানুষকে একাগ্রচিত্তে নামাজ আদায়ের শিক্ষা দেন। এ প্রসঙ্গে হাদিস শলীফে বর্ণিত হয়েছে উচ্চারনঃ লা সালাতা ইল্লা বি হুজুরীল ক্বালব। অর্থ ঃ একাগ্রতা বা হুজুরী দীল বিহনে নামাজ শুদ্ধ হয় না। মূলত একাগ্রতা বিহীন নামাজ আল্লাহ্র দরবারে কবুল হয় না।মুসলমানগন যাতে দুনিয়ার চিন্তা মুক্ত হয়ে একাগ্রতার সাথে আল্লাহ তায়ালাকে হাজির নাজির জেনে নামাজ আদায় করতে পারেন সূফী ম্রাট হুজুর কেবলাজান সেই পদ্ধতি শিক্ষা দেন।তাঁর নিয়ম অনুসরন করলে মুসুল্লিদের নামাজের দুনিয়ার কোনো চিন্তা আসে না্ফলে তারা নামাজে ফায়েজ বরকত ও রহমত হাসিল করতে পারেন।হযরত রাসুল সঃ ফরমান উচ্চারণঃ আসসালাতু মে রাজুল মু মেনিন। অর্থঃ নামাজ মু মেন ব্যক্তির জন্য মেরাজ। সূফী সম্রাট হুজুর কেবলাজানের শিক্ষা অনুযায়ী নামাজ আদায় করলে এ হাদিসের বাস্তবতা উপলব্দী করা যায়।,0,religion
এই নাস্তিকের বাচ্ছা গুলোকে ধরে ফাসি দেওয়া হয় না কেন ??,0,religion
যারা দেওয়ানবাগী হুজুরকে নিয়ে গালাগালি করছেন তাঁরা আল্লাহর মহা আজাব ওগজবের জন্য অপেক্ষা করেন। আল্লাহ বলেন যারা আমার অলীর সাথে শত্রুতা করে আমি আল্লাহ তার বিরুদ্ধে যুদ্ধ ঘোষনা করলাম হাদীসে কুদ্দুসী সুতরাং দেওযানবাগী হুজুর নন স্বয়ং আল্লাহর সাথে যুদ্ধের জন্য প্রস্তুত থাকুন। আল্লাহর সাথে যুদ্ধকরে টিকে থাকতে পারবেন ত?। আল্লাহ বলেন আল্লাহু ওলিউল্লাহজিনা আমানু অর্থাৎ আল্লাহ মুমিনদের অবিভাবক। আল কোরআন সুতরাং সারা বিশ্বের মানুষও যদি দেওয়ানবাগী হুজুরকে খারাপ বলে তাতে তার কিছুই আসে যায় না যদি তার মালিক তার পাশে থাকে। কারন কারো কথায় লোহা কখনো স্বর্ণ হয় না আবার স্বর্ণ কোন দিন লোহায় রুপান্তরিত হয় না।,0,religion
এই চ্যানেলটাই তো সরকার আর নাস্তিকদের দালাল! সুতরাং এরা তো ইসলামকে খাটো করার চেষ্টা করবেই! কিন্তু আফসোস এরা সবাই জ্ঞানি মূর্খ!,0,religion
জ্ঞান নাই যার তাদের সাথে কথা বলা ঠিক না,0,religion
স্যতান কিনা করে আদমকে দিয়ে । হে মানব ফিরে আস। হেতাহেত পাবে,0,religion
দুনিয়া আর বেশি দিন নেই,0,religion
নাস্তিক রা কি যুক্তি দেয় এগুলি??,0,religion
আল্লাহ তোমাদের শান্তিতে রাখুক,0,religion
সালারে আমগো এলাকা দেখলে জুতা পিটানি দিতাম।,0,religion
মিজানুর রহমান আমাদের দেশের ঘর্ব তাহেরি একটা বড় ভন্ড,0,religion
শিশু বক্তা কিয়ামতর আলামত তার প্রমান দেকেন,0,religion
হাহা আমার লজ্জা হয় যখন ওর মুখে শুনি বড় কথা,0,religion
মিজানুর রহমান আমার খুব পিয় আমার জদি এরোকম একটা ছেলে সন্তান মিজানুর রহমানের মত বানাইতাম । সবাই দোয়া করবেন আমার জেন ছেলে হয় ।,0,religion
তুই এই ভিডিও এক মাস হলো ছারছিস। তুই আসল শয়তান কারন তুই এই জায়গায় ওয়াজ করতে এসেছিস কারো গিবত গাইতে না। কারন তুই একটা বাচ্চা পোলা। কারা কি ওয়াজ করলো তোর সেইটা দেখার বিষয় নাই।তুই এই জায়গায় ওয়াজ করতে এসেছিস কোরআন শরীফ উপলক্ষে আলোচনা করবি তা না। তুই পথম থেকেই তাহেরির চা ঢালা খেককু খেককু চোদাও নাকি।তোক এই চিয়ারে বসার অনুমতি কে দিসে।আর কোন ওয়াজ করবিনা তুই কারন। তুই একটা শিক্ষা যোগ্যতা শিশু বক্তা হাফেজ।আল্লাহ্ কে ভয় কর পাঁচ ওয়াক্ত নামাজ পর আর নিজে ওয়াজ করতে পারলে ওয়াজ কর। কারো চা ঢালা ঢালী চোদাছ না।,0,religion
এই সালা আসলেই শয়তান এই শয়তান আল্লাহ রাসুল সা লাল এবং হলুদ রঙের পোশাক পুরুষের জন্য নিষেধ করেছেন অথচ তোর পাগড়ি হলুদ ভন্ডামি সিমা অতিক্রম করে গেছিস তোরা এই শয়তান হাজ্বীগন মাথা মুন্ডন করেনা? তুই যেভাবে চুল রাখছিস এভাবে রাখলেতো তদেরকে হাফ লেডিস মনে হবে আর রাসুল সা মেয়েদের বেশ ছেলেদের ধরতে নিষেধ করেছেন। হাদিসের ব্যাখ্যা কি আর তোরা বুঝাস কি হাদিস দ্বারা একদল হিন্দু এবং বৌদ্ধ সম্প্রদায়কে বুঝানো হয়েছে,0,religion
আল্লাহ বিচার করবে,0,religion
ওদের চাইতে সেফুদাই ভালো,0,religion
ড এনায়েত উল্লাহ অাব্বাসী যার নামের অাগে ডক্টর এবং সাইয়্যেদ ওনি উত্তর দিতে পারবে না🤧 বা ওনার জানা নাও থাকতে পারে এমন টাই বললেন পিছনের হিংসাত্মক মেী লোভী ব্যাক্তিটি গাদার মত দাঁড়িয়ে গেলেন শ্রোতাগন প্রশ্ন করতেছেন হজুর উওর দিচ্ছেন এরমধ্যেই কি ঘটল সবাই তু দেখল,0,religion
আল্লাহর আকার তো এই পৃথীবিতে দেখা যায় না তবে আখিরাতে সবাই দেখতে পাবে। আর দেওয়ানভাগি হালায় এটা কি বললো? 😃😂😹,0,religion
আল্লাহ আপনাকে নেক হায়াত দান করুক।যেন এরকম ভন্ডদের মুখোশ খুলতে পারেন।,0,religion
আব্বাসি বন্ডামি আর কত করবি,0,religion
জুতা দিয়া পিট সালারে।,0,religion
হাফিজুর রহমান তো বাংলা দেশের গোরব তাকে কেন ভন্ড বলুন ভাই,0,religion
আপনার শুরু থেকে আসি তাহসিনেশন। দেওয়ানবাগী হুজুর তালশহর মাদ্রাসার ভিপি ছিল তা আপনি উল্লেখ করেন নাই সালে তিনি উক্ত এলাকার জন সেচ্ছাসেবক নিয়ে মুক্তিযুদ্ধে যোগদান করেন পরে উনি সেক্টর কমান্ডার হিসেবে মুক্তিযুদ্ধ করেন। স্বাধীন বাংলায় সকল মুক্তিযোদ্ধাদের নিয়ে উনি ততকালীন রেসকোর্স ময়দানে প্রথম স্বাধীন বাংলায় ঈদের জামাত পরিচালনা করে যার ইমামতিও উনি নিজে করান। মুক্তিযুদ্ধের পরে বাংলাদেশ সেনাবাহিনীর অনুরোধে উনি আর্মিদের রিলেজিয়ার্স টিচার হিসেবে যোগ দেন। সেকেন্ড দেওয়ানবাগী হুজুর যার বাইয়াত নেন তার নাম ভুল উল্লেখ করেছেন তার আসল নাম ইমাম সৈয়দ আবুল ফযল সুলতান আহম্মদ। তৃতীয় আল্লাহর আকার নিয়ে আমার মোর্শেদ দেওয়ানবাগী বলেছেন আল্লাহর আকার আছে আপনে আপনার জ্ঞ্যান দিয়ে পারলে প্রমান করেন আল্লাহর আকার নাই!! চতুর্থ ই এপ্রিল ইসলাম ধর্মের পূর্নর জিবনকারী হবে না এইটা হবে ইসলাম ধর্মের পূনর্জিবন দানকারী। পঞ্চম দেওয়ানবাগী হুজুর যে স্বপ্নে দেখেছিলেন তা হলো ঢাকা থেকে ফরিদপুর পর্যন্ত একটি বাগান যা ছিল নোংরা রাসূল পাক স দেওয়ানবাগী হুজুরকে বলেন আপনি এই বাগানটি পরিষ্কার করে দিতে পারবেন? আমার মোর্শেদ কেবলা সাথে সাথে পরিষ্কারের কাজ শুরু করে দেন। তখন রাসূল পাক স বলেন এই বাগানটি আমার ধর্ম আর যে ময়লা ছিল তা ছিল আমার ধর্মের ময়লা যা আপনি পরিষ্কার করে দিয়েছেন। আপনি আমার ধর্ম আবার জীবন দিয়েছেন যেমন দিয়েছিল বড়পীর হযরত আব্দুল কাদের জিলানী খাজা মাইনুদ্দিন চিশতি। আপনি আমার ধর্মের পূর্নজিবন দান করেছেন। ষষ্ঠ উনার স্ত্রী কন্য আল্লাহকে দেখেছেন আপনি পারলে প্রমান করেন আল্লাহকে দেখা যায় না!!! সপ্তম উনার যে ভিডিও টি দিয়েছেন যতটুকু দিয়েছেন তার পরের টুকু দেন নাই এইটা একটি ছলনার আশ্রয় আপনি নিয়েছেন। ভাই লিখতে লিখতে হাত ব্যথা হয়া গেছে। আপনার অজ্ঞ্যতা আর মুর্খতা দেখে আমি দিলাম আপনার 👏👏👏👏👏👏👏👏👏👏👏👏👏 প্রথম যখন আপনি ষ্টিল পিক দিয়েছিলেন কামিংশুন তখনই আমি একটি কমেন্টে দিয়েছিলাম সম্ভবত আপনি দেখেন নাই। যাই হোক নাস্তিক নিয়ে একটি পোষ্ট দিয়েছিলেন আর বলেছিলেন যে এইসব মানুষ করে লাইক আর কমেন্টের জন্য। নিজেই এখন ওই একই উদ্দেশ্য নিয়ে একই কাজ করলেন। নিজের ফলোয়ার বাড়ানোর জন্য কমেন্টের জন্য। ডুলা কয় চালনিরে তোর বড় বড় ছেদ😅😅 ভাই হাসতে হাসতে পাপ করলে কানলেও যায় না। আপনের চাইতে আরো বড়োবড়ো হাত্তিঘোড়া আসছে দেওয়ানবাগীর বিরুদ্ধে আমাদের দরবারের সামনে একুশে টেলিভিশনের ক্যামেরা ফিট করছে মোল্লারা দেওয়ানবাগের প্রতিটা ইটা খুইল্লা নিয়া যাইব আর উনারা তা লাইভ দেখাইব তা তো হয়ই নাই বরং যেইসব মোল্লারা আসছিল দেওয়ানবাগ ভাংতে আজকে তারাই ছাত্র বলতকার কইরা ধরা খাচ্ছে ছাত্রী ধর্ষণ কইরা মাথা কাটা যাচ্ছে কেউ একাত্তরের দালাল উপাধি পাইছে কারো যুদ্ধ অপরাধের জন্য ফাসি হইছে কেউ আবার প্রহর গুনতাছে কবে তার ও যেন ফাসি হয়া যায় 😂😂😂 আল্লাহর হাতে বোথা দাও অস্তে অস্তে করে ঘাও। যারা নেতৃত্ব দিয়েছিল দেওয়ানবাগ দরবার শরীফ ভাংচুরের জন্য তারা আজ কোথায়? হাত্তিঘোড়া গেল তল আর আপনি আইছেন পিপড়া বলে কতো জল? 🤣🤣🤣 আপনারে চিন্তা করছিলাম আনফলো কইরা দিব কিন্তু ভাবলাম আপনার ফলোয়ার থাকলেই আপনার সাথে আল্লাহ কিরুপে খেলে তা দেখার জন্য হলেও আপনার সাথে কানেক্ট থাকি😘😘 পরিশেষে পাপ করে মাফ যে চায় সে আল্লাহর প্রিয়। আর পাপ করে তার উপর স্থির যে থাকে সে শয়তান। আপনি যদি দেওয়ানবাগী নিয়া সত্য জানতে চান তাহলে আমার সাথে যোগাযোগ কইরেন আর যদি ব্যবসায়িক উদ্দেশ্যে আরেকজনকে ভিডিও বানান তাহলে কিছু বলার নাই। তবে দেইখেন যেমন নাচন কোদন আর অভিনয় করে দেওয়ানবাগী হুজুরকে হেয় করার চেষ্টা করেছেন আল্লাহ যদি আবার আপনার সাথে এমন নাচন কোদন আর অভিনয় করে আপনি কই থাকবেন। তবে আল্লাহ দয়ালু আর আল্লাহকে দয়ার রুপেই থাকতে দিয়েন। আবার বললাম যদি সত্য সন্ধানী হয়ে থাকেন তাহলে সত্য প্রচার করেন,0,religion
তাসিন ভাইয়ের এক নম্বর ভক্তরা লাইক দিয়ে পালিয়ে যাও👍,0,religion
ঠিক কথা বললে আগুন ধরে,0,religion
সত্য মিথ্যা যাচাই করে প্রচার করা উচিত। এই ভিডিও তে তো বুজলাম না যে দেওয়ানবাগী ভন্ড। সঠিক তথ্য তো আজও পেলাম না। শুধু শুনি প্রমান তো পাইনা। যদি একদম সঠিক প্রমান হাতে থাকে তবে প্রমান সহ ভিডিও দেন তো দেখি। কিছুদিন আগে শুনলাম এবং ইউটিউবে দেখলাম দেওয়ানবাগী মারা গেছেন এবং কপিনের ছবিও দেখলাম এবংশুনলাম দেওয়ানবাগীর মৃত্যু খুসি মিষ্টি ভিতরন করছে।তারপর দেখি ও শুনি দেওয়ানবাগী বেচে আছেন। এবং সম্পূর্ন সুস্ত। এতে কি প্রমান হয়। শুনলাম দেওয়ানবাগী মা ফাতেমাকে বিয়ে করেছেন। কি মিয়ারা মা ফাতেমা দুনিয়া থেকে বিদায় নিয়েছেন সারে শত বৎসর আগে আর দেওয়ান বাগী এখনো জীবিত। আমার প্রশ্ন হলো বৎসর আগের মৃত ব্যক্তিকে কি কেউ বর্তমানে বিয়ে করতে পারে? এ ই ইউটিভে প্রচার করেছে। পরিশেষে বলি যারা বলে দেওয়ানবাগী ভন্ড তাদের এক কথাও বিশ্বাস করতে হবে যে দেওয়ানবাগী মৃত । লাশ ও দাপন কাফনের ছবি সহ ভিডিও করে পোষ্ট করে। কিন্তু দেওয়ানবাগী মৃত। কিন্তু তিনি আজও সুস্ত। ঠান্ডা মাথায় যদি কেউ একটু ভেবে দেখেন তবে বুজতে পারবেন। এদের মতো কিছু জঙ্গি গুষ্টিরাই দেওয়ানবাগীর বিরুদ্ধে একের পর এক মিথ্যা তথ্য প্রচার করে আর সাধারন মানুষ চিন্তা ভাবনা ছাড়াই ঠিক ঠিক করে যাচ্ছে আজ কোন মায়ের সন্তান পারেনি দেওয়ানবাগী যে ভন্ড তার একটিও প্রমান দিতে। দেওয়ানবাগ দরবারের একটি ঘোষনা দেওয়া আছে যে দেওয়ানবাগীর একটি কথারও যদি কেউ ভুল প্রমান করতে পারে তাকে লক্ষ টাকা পুষ্কার দেয়া হবে। কই আজ শুনিনি কেউ আসতে। এই ছেলেদের মতো কিছু কুলাংগারের দল দেওয়ানবাগীর বিরুদ্ধে একের পর এক মাথ্যা তথ্য প্রচার করেই যাচ্ছে। তাই আমি বলি রাগা রাগি বা গালাগালি নয়। সত্য জানুন। যারা জারজ ঠিক তারাই মিথ্যাচার করে। যদি পারেন তো প্রমান দেখান প্রমান করুন।,0,religion
এডমিন ভাই আপনি কি পাগল হইতাছেন নাকি কেন সাধারণ মানুষকেকে এভাবে পাগল বানাইতে চাইতেছেন,0,religion
তালি দিসি ভাই।,0,religion
আরে মাজার পূজারী ভন্ড কয় কি,0,religion
এইটা একটা ভণ্ড চয়তানৰ ভাব লোতচাৰ ঠিকাদাৰ ই নৰপিশাচ,0,religion
পাগল ছাগল এ দুনিয়া ভুলে গেছে,0,religion
তিন জন নাস্তিককে জুতার মালা দেয়া দরকার,0,religion
নাউজুবিল্লাহ এইসব ভন্ড বাংলাদেশে থাকে কেমনে 😡😡😡😡,0,religion
বক্তা সত্যিই বলছেন মাজার পুজারীকে চল্লিশ দিন মসজিদে গিয়ে জাম্মাতের সহিত নামাজ পড়তে বলুন ।ইনশাআল্লাহ ওনি আর মাজার পুজারী থাকবে না,0,religion
অলিদের আপনি ভন্ড বললেন আপনি কি বুঝে বললেন? শাহ পরান শাহ জালাল শাহ আলী এরা কি ভন্ড? এরা ভন্ড হলে ইসলাম কি তোর বাপ আনছে শেষে সালাম টা ঠিক মতো শিখোছ নাই,0,religion
অতিরিক্ত রসিকতা তামাশা ঠাট্টা নিষিদ্ধ অল্প রসিকতা শালীন বাক্য দ্বারা অনুমোদিত আহলুলবাইত আঃ রাসূলুল্লাহ সঃ থেকে তামাশা হচ্ছে ছোট ধরনের অপমান। যে কেউ খুব বেশী রসিকতা করে সে অজ্ঞ বলে বিবেচিত। যখনই কেউ একটি তামাশা করে তখন সে তার বুদ্ধি থেকে কিছুটা দূরে সরে যাই। বেশি তামাশা করো না মানুষের সাথে কারণ তারা তোমার উপর স্বাধীনতা পেয়ে যাবে। যখনই একজন মানুষ একটি তামাশা করে তার বুদ্ধির একটি অংশ নির্গত হয় । যখনই একজন ব্যক্তি একটি কৌতুক করে সে তার বুদ্ধির একটি অংশ থেকে বেরিয়ে যাই। যখন তুমি কাউকে ভালোবাস তখন তার সাথে বেশি কৌতুক করবে না বা তার সাথে বেশি বিতর্ক করবে না। যে কেউ বেশি কথা বলে তার আবোল তাবোল কথা বাড়ায় এবং যে বেশি রসিকতা করে তার নিবুদ্ধিতা বৃদ্ধি পায়। রসিকতা মজার বর্ণনা এবং নিরর্থক বক্তৃতা থেকে দূরে থাকো তাতে তোমার আত্মসম্মান বজায় থাকবে। যে কেউ বেশি কৌতুক করে তার গম্ভীরতা গুরুত্ব অকার্যকর হয়ে ওঠে এবং তার গুরুত্বপূর্ণ কথাও রসিকতা হিসাবে বিবেচিত হয় । যে কেউ অতিরিক্ত রসিকতা করে তার বিরুদ্ধে কারো না কারো ক্ষোভ ঘনীভূত হতে থাকে এবং তাকে সে গুরুত্বের সাথে নেয়না । তিক্ততার সাথে বিতর্ক করবেন না তাতে তোমার গৌরব নষ্ট হবে বা তিক্ততার সাথে রসিকতা করো না কারণ তারা অন্যেরা তোমার উপর স্বাধীনতা নেবে। অতিরিক্ত হেসো না তাতে শ্রদ্ধা হারাবে এবং খুব বেশী তামাশা করো না ফলে তোমাকে হালকাভাবে গ্রহণ করা হবে । অনুগ্রহ প্রদান করো হও তুমি ধন্যবাদের যোগ্য হবে ভয় করো আল্লাহকে তাঁর আইন ভাঙ্গাকে লোকেরা তোমাকে ভয় করবে অতিরিক্ত মানুষের সাথে রসিকতা করো না কারণ ফলে তোমাকে হালকাভাবে গ্রহণ করা হবে । সর্বশক্তিমান আল্লাহ তাকে ভালোবাসেন যে রসিকতা করে অশালীন বাক্য ব্যবহার করা ছাড়া যখন একা থাকে তখন সে ভাবে অন্যদের কাছ থেকে শিক্ষা গ্রহণ করেন এবং রাতে এবাদত করে । মানুষের সাথে রসিকতা করো না কারণ একটি সম্মান এবং মর্যাদা নষ্ট করবে। রাসূলুল্লাহ সঃ এর সাহাবীরা একত্রিত হতেন এবং তারা বিভিন্ন রসিকতা করতেন তখন নিম্নোক্ত আয়াতটি নাজিল হয় যারা মুমিন তাদের জন্যে কি আল্লাহর স্মরণে এবং যে সত্য অবর্তীর্ণ হয়েছে তার কারণে হৃদয় বিগলিত হওয়ার সময় আসেনি? পবিত্র কুরআন ? তারপর নবী সঃ এই আয়াতটি তেলওয়াত করলেন করলেন তারা তাদের কৌতুক ও অসার কথা বন্ধ করে দিল।,0,religion
ভাই বর্তমান সময়ের সবচেয়ে বড় ফিৎনা হচ্ছে হেযবুত তাওহিদ। আশা করছি আগামি টপিকে হেযবুত তাওহিদ এর রোস্ট আসবে,0,religion
ঠিক মত ই তুলে ধরেছেন ভন্ডদের সবগুলা রাবিস,0,religion
চার জন নাস্তিক এর মধ্যতো একজন উলঙ্গ,0,religion
গর্দভ উপস্থাপক এবং গর্দভ নাস্তিক,0,religion
জাওরা শিশুবক্তা,0,religion
এই খালার ঘরে খালারে কেটা কয়ছে ওয়াজ করতে,0,religion
উপস্থাপিকা ফালতু,0,religion
গালি না দিয়া ওনার ভুল ওয়াজ মাজার দরবার পরিহার করুন। গালি দিয়ে আপনি খামাখা একটি পাপের বোঝা বাড়ালেন। পাড়লে দোয়া করুন যেন আল্লাহ তাকে হেদায়েত দান করেন।,0,religion
দেলোয়ার হোসাইন সাঈদি বাইরে থাকলে তোর মত তাহিরিকে জুতা দিয়ে পাঠাইতো সালা ফেরাউনের পোলা,0,religion
এই বাচ্চাটির কি এমন জ্ঞান হয়েছে,0,religion
মিজানুর রহমান ভন্ড তো আছেই এক নাম্বার মুনাফিক সালা ওহাবিও না সুন্নিও না,0,religion
এই ভিডিও বানানোর জন্য ধন্যবাদ,0,religion
প্রমান আছে এডমিন সাহেব,0,religion
ভন্ডদের মুখোশ উন্মোচন করুন সাথে আছি সাথে থাকবো,0,religion
শয়তানটার মুখোশ উন্মোচন করে ভাল একটি কাজ করলেন ।,0,religion
আলোচনার বিষয় হলো কবর ও হাশর আর উনি করতেছে পাগলের বয়ান ।,0,religion
থোখের ভাসাটা কি,0,religion
সালাকে কেও চায়না তারপরও ফতুয়া দিতে আসে,0,religion
যে পীর মেয়ে লোকের খিদমত নেয় সেই পীরকে মুড়ো ঝাটা দিয়ে ঝাটিয়ে দিন কোনো গোনাহ হবে না,0,religion
আমির আলেম,0,religion
বাংলাদেশটা কে ধবংস করে দিচ্ছে এই পাগলা,0,religion
সালায়  ভন্ড,0,religion
আরে প্রতিবন্ধী যার ব্যাপারে মন্তব্য করলি তার সমান যোগ্যতা অর্জন কর আগে তারপর তার ব্যাপারে মন্তব্য কর,0,religion
ওটা তুর মায়ের জামাইর ছবি,0,religion
এই বেয়াদব তাবলীগ জামাতের বিরুদ্ধে কিছু বলবিনা তাবলীগ জামাতের একটি আলেমের সমতুল্য তিনি তাদের যত সোজা করার মত তৃহউস কখনো,0,religion
এই ভন্ড তাহেরিকে মাহফিলে দাওয়াত দেয় কেন,0,religion
মোরগি কবির কে জুতা মারু হালাই কাফের,0,religion
ঠিকে আছে অপমান করা,0,religion
এই কাফের টা আমাদের ইসলাম টাকে নষ্ট করে দিচ্ছে । ধন্যবাদ তাসিন ভাই।,0,religion
মহিলা না কি,0,religion
সালাকে জুতা মারলে? ????,0,religion
আটরসির ভক্তরা শুধু হূ হূ হূ তো করছে এরা আল্লাহ কে ডাকছে কখন??,0,religion
তোম‍রা ওকে মেরে ফেলো বাংলা দেশি,0,religion
ভন্ড তাহিরী টেজে মেকাফ করে উঠেন কেন তিনি কি হিজরা,0,religion
শুধু চার জন নাস্তিক নয় চার কোটি নাস্তিক আসলেও একজন আলেমের সাথে হার মানবে!,0,religion
কুকুরের বাচ্চা,0,religion
ওই গুলা সত্যি ভন্ড,0,religion
ওই সালার পোলা কাকে কী বললি তোর মাথার তার কয়টা চিরচে তোকে হেদায়েত দান করক। পৃথিবীতে কোন মাওলানা কী মহান আল্লাহ কে গালি দিবে তোদের মতো কিছু সয়তান দের কারনে এমর হয়।,0,religion
গরু কবির গরু এ রয়ে গেল,0,religion
মিজান ভাই মানুষকে কুকুর বলা ঠিক না,0,religion
আপনাকে ভাই অনেক অনেক ধন্যবাদ,0,religion
ভাই ভিডিও টি ভালো লাগলো।,0,religion
ফেতনা তোমরাই তৈরি কর তুমি কি ওয়াক্ত নামাজ পর নিজের চিন্তা কর।,0,religion
ওই মিয়া ভন্ডামি করার জন্য এই চেনেল খোলছেন নাকি।মানুষকে ভিবভ্রানত করেন??,0,religion
বোখারীর হাদীস খোতবা চলার সময় একজন সাহাবি এসে মসজিদে বসে গেলেন নবী বল্লেন দুই রাকাত নামাজ আদায় করে তারপর বস আর হালায় বলে খোতবা সময় নামাজ আদায় করা জাবেনা,0,religion
কুকুরের বাচ্চাগুলো ক্ষেপেছে,0,religion
আললা তোমার গজব ডাল ওদের ওপর 😭😭😭😭😭😭😭😭,0,religion
তুই একটা সয়তান।,0,religion
এইটা জিকির না সয়তানি জুতা দিয়ে পিটানো দরকার,0,religion
সহি ইসলাম এটাই হুজুরকে আল্লাহ নেক হায়াত দান করুক আমিন,0,religion
আল্লাহ তুমি এদের কে হেদায়াত করুন।,0,religion
যে এই ভিডিও টির উপরে যে মাজার পুজারি কথাটা লিখেছে সে আসলে এজিদ পুজারী,0,religion
দেওয়ানবাগীর আস্তানা ভেঙ্গে দেও জ্বালিয়ে দেও😡😡😡😡,0,religion
ভাই গো কোন প্রমাণ ছাড়াই এরা ভন্ড,0,religion
শে জা করক ওখানে আল্লাহর নাম আছে,0,religion
জাতা,0,religion
ভুল হলে তোমরা আলেমরা এক জায়গায় বসে তা সমাদান কর। কেন আপনারা জনগনকে বিভ্রান্তি করেন। বিশেষ করে আহলে হাদিস বক্তারা আপনারা সমালোচনা বন্ধ করুন।,0,religion
এদের নিয়া পচাইয়া ভিডিও বানান এমোন ভাবে ভিডিও বানান যে এদেরকে মানুষ যেন শুধু গ্রিনাই করে,0,religion
এদেরপাঠাবলিদেওয়াহবেএকসময়,0,religion
ভাই আমি তো আপনারা ছিলাম আজ থেকে আমার মা ও আপনার হয়ে গেসে আর আমার আম্মুর পক্ষ থেকে আপনাকে ধন্যবাদ,0,religion
তাহেরিকি আপনার সাথে কিছু করেছেন,0,religion
আপনি কি ভালো মানুষ,0,religion
এইসব ভন্ডদের মুখোশ খুলে দেওয়া অতি জরুরী কারন এরা সাধারণ সহজ সরল মানুষের ঈমান নষ্ট করছে।,0,religion
দেওয়ান বাগীকে জবাই করা হোক,0,religion
আলহামদুলিল্লাহ্‌ আল্লাহ আমাদেরকে আমির হামজার মতো একজন আলেম দান করেছেন।,0,religion
আমার বাড়ী আসাম আমি আসাম থেকে বলছি মিজানুর রহমান আজাহারী ওয়াজ খুব ভালো লাগে,0,religion
উনি রসুল সা কে মুসলিম না এবং ইমানদার না এই কথা বলেছেন 😡😡,0,religion
জুতা দিয়া মারার দরকার তোরে জারদ সন্তান,0,religion
সবকিছুর বিচার করবেন মহান আল্লাহতালা,0,religion
পাডা বক্তা থামাতে পারে না,0,religion
সালার নাস্তিক,0,religion
সামনে হালুয়া রুটি দিলে আব্বাসি উঠতোনা এরা সব সাহালি বাবা ফতে বাবার পাগল এগুলির ওয়াজ শুনে কোন ছাগলে,0,religion
হে আল্লাহ আমাদের সবাই কে হেদায়েত দান করো,0,religion
আমি আল্লাহর কাছে দোয়া করি । হয় এই নাস্তিক দের হেদায়েত করুন।আর না হয় এদের ধংস করেন,0,religion
বাংলাদেশের পুলিশ এগুলো দেখেনা কেন এই ভন্ড কে আজীবন রিমান্ডে রাখা প্রয়োজন !!,0,religion
ভাল হও,0,religion
তাহেরির দোষটা আসলে কোথায় বুঝতে পারলাম না! সে কি মদ খায়? সে কি জুয়া খেলে? তার স্ত্রী কি তার চারিত্রিক ব্যাপারে কোন অভিযোগ করেছে? সে কি সুদের কারবার করে? সে কি চুরিডাকাতি করেছে? সে কি অন্যের সম্পত্তি হরণ করেছে? সে কি শুয়োর বা অন্য কোন হারাম জন্তুর গোশত খায়? সে কি মসজিদ মাদ্রাসার তহবিল তসরুফ করেছে? সে কি ধর্ষণ বলাতকারে লিপ্ত? সে কি নামাজ রোজা বা শরিয়তের ফরজ বা ওয়াজিব অস্বীকার করেছে? মিথ্যারোপ করে কাউকে ছোট করা হয়তো যেতে পারে আপনি বড় হতে পারেন কি?,0,religion
এই খবরের সত্যতা কী?,0,religion
ভাইয়া আপনি সত্য কথা গুলো তুলে ধরার জন্য অনেক অনেক ধন্যবাদ,0,religion
তোমাকে হাজার সালাম।,0,religion
আসালামুআলাইকুম হুজুর আপনার কথা সত্য। আপনি সত্য তুলে ধরেছেন জারা সঠিক ইসলামের তালিম নেয়নি তারা কি করে সত্য মিথ্যা বুঝবে এদের কে আললাহ সত্য বুঝার তউফিক দান করুন। আমার বাড়ী সিলেটে আমরা দেখেছি হযরত শাহ জালাল শাহ পরান শুধু নয় আর বহুত মাজার আছে এগোলাতে উরোস হয় গান বাজনা গাজা মদ মেয়ে লোক গান গায় ডেন্স করে। আললাহ্ এদের সঠিক পথে ফিরিয়ে আনো নয়তো এদের দংশ করে দাও এরা ইসলাম ধর্ম কে কলংকিত করতেছে।,0,religion
কিছু জারব সন্তান এগুলো করে বাইনঞ্চদ,0,religion
তোমাদের টপিকটা ঠিক আছে চালিয়ে যাও ৷,0,religion
তেহেরি তোমাকে জুতা মারবো তুমি মিজানুর রহমানে জুতার জুক্তা হইবা না,0,religion
ভাই এই হল আমাদের বাংলাদেশ।। এখানকার বড় বড় রুই কাতলারা কেন দেওয়াবাগির সম্পর্কে চুপ করে আছে?? দেশটা কি দেওয়ানবাগির নাকি?? ইসলামের শত্রুর বিরুদ্ধে আমাদের শোচ্চার হওয়া প্রয়োজন।।।,0,religion
ভাই আমার কাছে কেনো জুতা নাই যে দিয়ে তোকে পিটাবো সালা,0,religion
ভন্ডটা টাকা দিয়া ইস্টিক খায় তাই এমন করে,0,religion
টাকা কামানোর ধান্দা।পাকা চোর,0,religion
যুক্তিক।,0,religion
তাহেরী তোকে পাইলে জুতা পিটা করবো। বদমাশ।তুই কেমনে মিজানুর রহমান আজহারীকে এগুলা বলস। তুই ভন্ড,0,religion
আল্লাহ তাদের হিদায়েত করে।,0,religion
এই হারামীটার প্রকাশ্রে ফাঁসি দেওয়া উচিত।,0,religion
মাথাই পুরাই আগুন ধরে গেছে নাস্তিক গুলির কথা শুনে,0,religion
কি বলবো বুঝতে পারছি না,0,religion
তে তেলাপোকার রং কি???,0,religion
দেয়ান।বাগিকে।জুতামারারদরকার,0,religion
মিজানুর রহমান আযাহারী ওয়াজ করেন তিনি ম ইস্তান অধিকার করেছেন😍😍😍😍,0,religion
মাজার পূজারীকে লাঠি দিয়ে মার,0,religion
আল্লার আমাদের তুমি হেফাজত করুক আমিন,0,religion
পুরান নাস্তিকের বাত নাই নতুন নাস্তিকের আমদানি।,0,religion
চার,0,religion
ভালো পথে ফিরে এসো সময় থাকতে আর কোন ভনডামি করোনা কুরআনের আয়াত সুনিয়ে মানুষদের বুজাও তবে তুমার ভালো হবে,0,religion
ভাই আপনাকে অনেক ধন্যবাদ ওকে ফাঁসি দেওয়া উচিত,0,religion
এখন কার বক্তারা অয়াজ নাদ দিয়া এসব বলে সম্সা সিস্টি করে,0,religion
ফাসি চাই।,0,religion
এই ভাবে নাচানাছি করলে যদি ভিসা পাসপোর্ট পাওয়া যায় তাহলে আমি নাচতে রাজি আছি!!,0,religion
এগুলা ওয়াজ নাকি আওয়াজ?,0,religion
দেখুন ভাই শিক্ষিত জ্ঞানী আর মূর্খ জ্ঞানের পার্থক্যটা এই ভিডিও দেখলে বোঝা যায় অশিক্ষিত অশিক্ষিত হয় তাদের কোন জ্ঞান থাকেনা আল্লাহর রাসূল অশিক্ষিতদের কে ঘৃণা করতেন কারণ তারা কোন কিছুকে নির্দিষ্ট করতে পারত না আসলে কোনটা ঠিক আর কোনটা ভুল শিক্ষিত বলতে শেখা আর জ্ঞান বলতে শেখা টা কে সঠিকভাবে কাজে লাগানো কিন্তু মূর্খদের ভিতর তো শেখার আগ্রহ কম আর আর জ্ঞান বলতে গেলে এদের একদম,0,religion
বাপ।বেটা্।এদেরকাচে।মুরখরা। যায়।জাহাননামি্রা,0,religion
ওদের আল্লাহ মাফ করবে না,0,religion
তাহেরি ভন্ড আমি মিজানুর রহমান কে ভালোবাসি।,0,religion
কিতাবে আছে ইসলাম মানে শান্তি বাস্তবে তার উল্টো লক্ষ লক্ষ মুসলিম ইসলামি দেশ ছেডে পাডি দিচ্ছ অমুসলিম দেশে। যে দেশে মুসলিম নাই ঐ দেশের মানুষ অনেক শান্তিতে আছে। কোন এক সময় বাংলাদেশ ও অনেক শান্তিতে ছিল যখন মুসলমান ছিলোনা। যেই মাত্র ইসলাম নামক অশান্তি বাংলায় প্রবেশ করলো শুরু হয়ে গেলো শুয়রের মতো জনসংখ্যা জন্ম দেওয়া।,0,religion
তর মতো হুজুর জগরা লাগাণের জণো আইসস কারন জারা পথম থেকে দেখবে ওআজ সুণবে গা জলবে কারণ তুই বুজাইআ বলতে পারস নাই পরে বলো সাহা জালালের কথা আগে ত্রদরণের কথা বলা দরকার ছিলো পরে লাইণের কথা বলসো চরমণাই কি করে দেখণা বাস বাইতে থাকে সেটাকে কি বলে ছাগল,0,religion
করুন পাবা,0,religion
না হুমায়ুন আজাদ এতো বড় ক্রাক মাতাল ছিল,0,religion
আবে অই তুমাদের চেনেলকে বলে দিতে চাই এসব ভন্ডামি ছার। হাফিযুর রহমান হুজুর টিকই বলসে।তুমরা আসলে কিছু বুজ না তাই এসব খারাপ কথা আজকাল এইসব সোসাল মিডিয়ায় ছার।তুমাদের বলে দিতে চাই আলেমদের সম্পর্কে যা জান না তা নিয়ে উলটা পালটা কথা বইল না।আলাহর কাছে তওবা কর।,0,religion
আল্লাহ তোদের বিচার করুক।নাস্তিক,0,religion
পাশের বাসার আন্টিরা একদিন দাওয়াত দিয়ে বলল মিলাদ আছে। আইসো । গিয়ে দেখি দুরূদ শরীয়ে ইবরাহীম আঃ র জায়গায় ইমাম মাহদী বলছে সবাই। সাথে সাথে বুঝে টয়লেটে যাওয়ার কথা বলে চলে আসলাম। পিডানো দরকার ছিল ওগুলারে,0,religion
এইসব বানরদের পিছনে রেখে হাসিনা বু বু তাহাজ্জুদ নামাজ এর ইমামতি করেন। এরাই হাসিনা আপার আসল মুরিদান।,0,religion
♥♥♥ভাই আপনাদের অসংখ্য মোবারক বাদ ও ধন্যবাদ♥♥♥ ভন্ডদের এরুপ আকাম কুকাম প্রকাশের জন্য ♥♥♥ ।,0,religion
আল্লাহ আমাদের সকলকে হেদায়েত দান করেন আমিন,0,religion
আল্লাহ্‌ হেদায়েত দেন,0,religion
এমন ভন্ডাদের আমরা বাংলার জমিনে দেখতে চাই না😡😡😡😡,0,religion
এসব যুক্তি কোন বোকা ছাড়া আর কে দিতে পারে না কারণ কোরআনে আছে বসে দাঁড়িয়ে অর্থাৎ যেভাবে পারেন জিকির করা জায়েজ কিন্তু এটা তো লিখা নাই জিকিরের মধ্যে বলতে হবে বসেন বা দাঁড়িয়ে যান বা শুয়ে পড়ুন এটা লিখা নাই যুক্তি দিয়েছেন ভালো কিন্তু না বুঝেই যুক্তি দেওয়াটা ঠিক নয়,0,religion
আপনারা যা বলেন লোকে তা শুনে আগে আপনারা আলেম রা ঠিক হন তার পর আমরা ঠিক হব,0,religion
এইসব জানোয়ার কে এনে হাত পা বেঁধে উপর দিকে তুলে নিচে আগুন দেওয়া দরকার বেশি না কমনা এমন ভাবে আগুন দেওয়া দরকার যাতে শরীরের চর্বি গলে গলে নিচে পড়ে,0,religion
এই সবগুল স্নাতিক,0,religion
ঠিক কয়ছেন আসলো ভন্ড,0,religion
চার নাস্তিক জুতা মারা উচিত,0,religion
আরে ভাইয়েরা ও বোনেরা আপনারা যে এই কমেন্ট করেন না কেন ওরা ফেমাস হতে চাই একটা কথা আছে না যে তোরা যে যা বলিস ভাই আমি ফেমাস হতে চাই ফেমাস হতে চাই,0,religion
জুতি পিটা করতে হবে,0,religion
যুগে যুগে এরকম কুলাংগার তৈরী হয়েছিল। তারা ইসলামে কোন ক্ষতি করতে পারে নাই। কেয়ামত পর্যন্ত পরবে না। বরং তারাই ক্ষতিগ্রস্ত হবে। ইংশাআল্লহ্,0,religion
তুই বাচ্চা পোলাপান যাকাত ফিতরা খাইয়া ভালো কথা তোর মুখে আসবে না এটাই স্বাভাবিক।,0,religion
পতিতালয় অনুমোদন না দিয়ে দাশী প্রথাটা চালু করলে অনেক মানুষ গুনাহ থেকে রক্ষা পাইতো। আর একটা সরকারি বাজার নির্ধারণ থাকতো যেখানে দাশ দাশী বেচাকেনা হতো তাহলে মানুষ বড়ো ধরনের গুনাহ থেকে বাচতো।,0,religion
এডমিন একজন বানোয়াট অভিযোগকারি। কারন সে দেওয়ানবাগী হুজুরের নামে বানোয়াট এডিটিং করা ভিডিও ছেড়ে নিজের ইচ্ছেমত বানোয়াট মিথ্যা কথা বলতেছে।এডমিন হয়তো জানেন না কারো সম্পর্কে বানোয়াট অভিযোগ আননে কি হয়?দেখুন যে ব্যক্তি কোন গোষ্ঠীর বিরুদ্ধে কোন বানোয়াট অভিযোগ আনল সেযেন নিজেই নিজের স্থান জাহান্নামে করে নিল সহীহ বুখারী,0,religion
কেউ যদি ইসলাম ত্যাগ করে এবং ইসলাম নিয়ে বাজে মন্তব্য করে তাহলে তাকে হত্যা করতে হবে,0,religion
তোমার বয়স কত ভাই কি করে বক্তা হয়লা,0,religion
তুই কাট মোল্লা,0,religion
হুজুরের কাছে আমার একটা প্রশ্ন আজানের টান গুলো এত ব্যাকা করেন কেন দয়া কিছু মনে করবেন না,0,religion
আমার কথা হল এই রকম গাজাকুর ইষ্টেজে বসে কিভাবে জুতা পিটা দিছে ভাল হইছে,0,religion
আপনি অনেক কথা বলেন কথা একটু কম বলে ভিডিও দেখান বুজলেন বাচাল রোসটার,0,religion
জুতা পিঠা করে নাই কেন???,0,religion
অাব্বাসির মত একটা ভন্ড শয়তানকে মানুষ কেন ওয়াজ করার জন্য নেয় বোঝি না দোষ কি অাব্বাসির নাকি যারা তারে মাফিলে ভন্ডামি করার সুযোগ করে দেয় তাদের। অাল্লাহ সবাইকে নেক বোঝ দান করো,0,religion
তুই তুর মাকে বিবাহ করিস,0,religion
অনেক দিন ধরেই অপেক্ষা করতেছিলাম এই ভন্ডটারে ধইরা কেউ লেংটা করুক আলহামদুলিল্লাহ ধন্যবাদ ভাই😍😍😍,0,religion
আরে ভাই সূরা বাকেরা আয়াতের কথা বলছে বুঝেন না কেউ তো সময় নিয়ে সূরা বাকেরার নাম্বার আয়াত খুজতে যাবে না তাই একরা আবাল কথা বলে দিছে,0,religion
আরে তোর তো এখনো সুন্নাতে খতনাই হয়নি,0,religion
ভাই আপনি চালিয়ে যান এবং সাবদানে থাকিয়ে। দোয়া করি এগিয়ে যান।,0,religion
কেও ত তর পক্ষে কথা বলে না,0,religion
খুব খাবার হুজুর কিছু য়ানে না,0,religion
তুর কন্ঠের উপর ঠাডা পরবো,0,religion
মামুনুল হক দাঃবাঃ এর মতো হতে হবে প্রত্যেক কে,0,religion
মামুন সাহেব তাদের সাথে না পারলে ওখানে গেলেন কেন মিয়া,0,religion
তাহেরির মার ভাতার কয়টা,0,religion
কোতাই আগরতলা আর কোতাই ছকিরতলা তাহেরী একজন বদমাইস আর মিজানুর রহমান আজহারী বাংলাদেশের একজন কোরআনের পাখি,0,religion
এই চার মুনাফিক কে জুতার মালা গলায় বিয়ে ঘুরাও,0,religion
আমি ভারত থেকে আব্দুল মালিক ময়না তদন্ত করে দেখা উচিত যদি ভন্ড তাহেরী সত্যিকারে ভন্ড হয় তাকে ফাঁসিতে ঝুলিয়ে দিয়ে মারা উচিত।,0,religion
তদের খাজা বালের বাবাকে বাচাবে কে,0,religion
আচ্ছা ভাই মুরগী চোর টোর বাদ দিয়ে আনবেন ওর দেখলে দিনটা ভালো যায়না,0,religion
উভয়ে দুজনেই মাজার পুজারী তবে ঠিকই আছে,0,religion
এসব ভিডিও সেয়ার করা ওচিত,0,religion
বসেন বসেন বাসি জান,0,religion
অনেক শুভকামনা রইলো তোমাদের জন্য,0,religion
আমার মনে হয় উনি ছাএী অবস্তায় দেখে তার ভাল ছাত্রী ছিলেন । মনে হয় আমার মত বাংলা কবিতার ব্যখ্যা গুলো ভালো লিখতেন ।,0,religion
এই ভণ্ড দের ভণ্ডামির জন্য বাংলাদেশের সরকার ও প্রশাসন সম্পূর্ণ ভাবে দায়ি। একটা মুসলিম দেশে এগুলো হয় কীভাবে?,0,religion
আল্লাহ আপনে এই ভন্ড দেরকে কতল করে দেন আমিন,0,religion
আবদুল খালেক সরিয়াত পুরী সে ও তো বন্ডো তার কথা বলেন না কেনো,0,religion
ভালো লাগছে ভিডিও টা।,0,religion
একটা লোক ফেইসবুকে নিজের মনগড়া মতো দেওয়ানবাগি হুজুরের বিরুদ্ধে যা খুশি তাই লিখে দিলো। আর আপনি সেই মিথ্যাবাদির পোষ্ট দেখে নাউজুবিল্লাহ বলে দিলেন? একবার কি নিজের চোখে এসে দেখে গেছেন দেওয়ানবাগি হুজুর কোরআন হাদিসের বিরুদ্ধে কথা বলে কিনা। ভাইয়া মিথ্যাবাদীদের কথা শুনে একটা ব্যাক্তিকে যা খুশি তা মন্তব্য করবেন না। মনে রাখবেন রাসূল সঃ এর জামানায়ও মিথ্যাবাদী লোক ছিলো বর্তমানেও আছে। তাদের কাজই অন্যর বিরুদ্ধে মিথ্যা কথা বলা,0,religion
আব্বাসীর ওয়াগ শুনলে ঈমান থাকবে না,0,religion
এ নাস্তিক কেনো এরকম হুজুর সেজে বসে আছে?এরা আসলে প্রকৃত ইসলামের দুশমন চক্রান্ত করে দেওয়ান বাগি নাম ধারন করেছে বেটা ইয়াহুদী কি করে কাবা ঘরের আকৃতি বানিয়ে হজ পালন হয়?নাউজুবিল্লা হজের মোহরা চলছে ইয়াগুদিরাও হাসবে,0,religion
তাহেরী হুজুর একজন হক্কানী আলেম,0,religion
এদের প্রত্যেক কে টা করে জুতার বাড়ি দেয়া হোক।,0,religion
হ্বক কথা খুব তিতারে আজকে সত্য কথা বললে কিছু নাম ধারীদের জ্বলে উঠে? কারন তারা তো মুসলমান হয়ে ইসলামের নাম দিয়ে ধর্ম ব্যবসা করে? আল্লাহ মাফ করোক সবাইকে হেদাইয়ত দান করোক এই চাচাকে জুতা পিতা করা দরকার চিল হাজার বিডিও আছে মাজারে কি চলতাছে? চাচার চোখে ঐ গুলো দেখেনা?,0,religion
এই রকম বক্তা সমাজের জন্য খুব জরুরী,0,religion
সবার প্রতি ভালোবাসা আমি নতুন চেনেল খুলছি পিল্জ সারস্কাইপ করুন!!♥♥,0,religion
নাস্তিকের বিরুদ্ধে আন্দোলন করতে পারে তাদেরকে মারতে পারে। বাট তাদের বিরুদ্ধে কোন আন্দোলন করতে দেখি না।,0,religion
মাশাআল্লাহ যেমন নামটা সুলতানি হুংকারটাও ছিল সুলতান এর মত,0,religion
আচ্ছা বাইয়া আপনারা কি মানু না,0,religion
আল্লাহ তুমি ওদের হেদায়েত দেও,0,religion
এতটা ফকিন্নি নিজে চলার মতো টাকা নেয় মানুশেরশাহাজজেচলেবকতা,0,religion
হাফিজুর রহমান হোজুরে ছবি সামনে কেনো,0,religion
ওর মনে হয় জম্নের ঠিক নাই অামি অান সাবসক্রাইব করছি অাসা করি অাপনারাও করবেন 😡😡,0,religion
জুতা মার গালে,0,religion
আমার প্রাণের প্রিয়ো মুসলিম ভাই আপনাদেরকে অনেক অনেক ধন্যবাদ এই ভণ্দামি গুলো প্রচার করার জন্য??,0,religion
জান বাচাইতে গিয়ে তাহেরী হুযুরের গজল গাইতে হল হাইরে বকতা,0,religion
দেওয়ান মাগীর ভক্তরা ডিজলাইক দিছে।,0,religion
চারটাই নাস্তিক,0,religion
উনারা সত্যানুসন্ধানি। ধর্মের অন্ধকার কুসংস্কার মিথ্যাচার ভণ্ডামি নৃশংসতা শয়তানি মূর্খতার বিরুদ্ধে উনারা একেকটা আলোর মশাল। উনাদের সত্যকে গলা চেপে ধরার জন্য যদি উনাদের কেউ খুন করেও তবু সে সত্য চেপে রাখা যাবেনা কোনদিন। কেননা সত্যের আগুন একদিন একদিন আগ্নেয়গিরির লাভার মত উদ্গিরন হবেই হবে।,0,religion
সম্পূর্ণ এডিটিং করা ভিডিও দিয়ে মানুষকে ধোকা দিয়ে কিছু টাকা ইনকাম করতে পারছেন। এই টাকা নিয়ে কবরে যেতে পারবেন কিনা একবার কি ভেবে দেখেছেন! আপনি ভাবার কথাও না কারন টাকা আপনার চোখ অন্ধ করে দিয়েছে।,0,religion
আমি একজনই আমার মনে হছে এদেরকে জুতো মারতে ইচ্ছা করছে,0,religion
হায়রে জাহেল গিয়াস তাহেরী,0,religion
দুস্ট উপস্থাপিকা এবং নাস্তিকদের সাথে কথা বলতে যাওয়াটা ঠিক নয়। এগুলো সব বেয়াদব,0,religion
আমাদের এই বাংলাদেশ ‌ এসব ভন্ড হুজুরের ‌ বিচার হয় না কেন? সরকার কি এদের দেখতে পাই না নাস্তিকদের?,0,religion
সব ঠিক আছে কিন্ত দাডিতে আগুন এটা করার দরকার নেই,0,religion
মিথ্যা কথা আর কত বলবেন,0,religion
এই ধরনের শিশু বক্তা যারা দাওয়াত করে নিঃসন্দেহে বুঝে নিতে হবে সেই এলাকায় কিয়ামতের আলামত চলতেছে। নিঃসন্দেহে বুঝতে হবে সেই এলাকায় মানুষ নামে মূর্খ গণ্ড ও সবাই কুসংস্কারে বসবাস করতেছে।,0,religion
আসতাগফিরুল্লাহ নাউযুবিল্লাহ,0,religion
বেগম খালেদা জিয়া তিন বারের প্রধান মন্ত্রী আর কাউয়া কাদের একজন রোড় মন্ত্রী। সুতরাং যেই প্রশ্ন করেছে সে হলো বেকুবের বড় বাবা।,0,politics
কাদের খালেদার জুতা,0,politics
মজাই মজা।।।,0,politics
তবে দলের সভাপতি পরিবর্তন আনা সর্বপ্রথম উত্তম কাজ দলের সভাপতি কি পরিবর্তন করা উচিত যত সমস্যা দলের সভাপতির কারণেই,0,politics
আওয়ামিলীগ ছাড়া বাংলাদেশের যুদ্ধাপরাধীদের বিচার আর কোনো দল করবে না এবং চিন্তাই করা যায় না যুদ্ধাপরাধীদের বিচার স্বচ্ছ হলেও তাদের ফাঁসি আবার অসচ্ছ হলেও ফাঁসি হবার কথা। অন্ততপক্ষে যে কয়েকজনের রায় হয়েছে। বিএনপি দ্বারা যুদ্ধাপরাধীদের বিচার তো দুরের কথা তাদেরকে রীতিমত রাষ্ট্র চালানোর দ্বায়িত্ব দিয়েছিল। সবচাইতে বড় কথা যুদ্ধাপরাধীরা আজ পর্যন্ত তাদের অপকর্ম বা ভূলের জন্য দেশবাসীর কাছে ক্ষমা চায়নি রাষ্ট্র চালনা ও রাজনৈতিক কৌশল নির্ধারণে হাসিনা খালেদা জিয়ার চাইতে অনেক পারদর্শী জনগণ আওয়ামিলীগ কে যে পছন্দ করে তা নয় তবে বিএনপির সময়েও ফিরে যেতে চায় না সত্যিকার অর্থে দেশে এখন বিএনপি কর্তৃক জোড়ালো আন্দোলন করার মত কোনো ইস্যু নেই।,0,politics
মাননীয় প্রধান মন্ত্রী কে ধন্যবাদ ইনু কে বাদ দেওয়ার কারণে জাসদ কে বাদিয়ে নিরবাচন করলে আওয়ামলীগের আরো ভালো হত তার কথায় প্রধান মন্ত্রী কে আপন করা হচ্ছে সৈয়দ আশরাফ বলেছেন সে বঙ্গবন্ধুর হত্যার সাথে জড়িত ছিল ।ইনু তর খাওয়া নেই আওয়ামলীগে ।,0,politics
হায়রে হলুদ মিডিয়া,0,politics
কাদের এর বৌ এর খবর নেওয়া হোক,0,politics
ছাত্র লীগ কে ভয়কোট করুন,0,politics
ঐক্য অ‌নৈ‌ক্যের মুল ।,0,politics
ভাই আমি একজন সাধারণ ছেলে এখনো ইনকাম করিনা। তারপর ও তো আমার মোবাইল এর দাম লাখ টাকা! আর সে তো মন্ত্রী। আচ্ছা যখন প্রিন্স মুসার ঘড়ির দাম যখন কোটি টাকা হয় তাহলে সবাই আপনারাই আমরাই বাহ বাহ করি। আমরা ও আপনিও সবাই স্বপ্ন দেখে কোটিপতি হওয়ার বা দাবি জিনিস ব্যবহার করা। কিন্তু আমরা পাইনা বা আমাদের কপালে নাই। তাই অন্যের দেখলে আমাদের জ্বলে। জ্বলবেই। স্বাভাবিক,0,politics
আওয়ামী লীগের যতগুলো নেতাকর্মী আছে তারা সবাই পাগলের মত হয়েছে এই মহিলাটা কি বলে গেল কার সাথে কার তুলনা করে দেখুন আপনারা কালাদা জিয়া হল একজন দেশনেত্রী দেশ প্রেমিক আর উনাকে নিয়ে ওবায়দুল কাদের সাথে তুলনা করে ওবায়দুল কাদের একটা ছাগলের বাচ্চা কি দরকার এসব কথা বলার ফারহানা আপু আপনাকে অনেক অনেক ধন্যবাদ এই পাগল মহিলাকে দাঁতভাঙা জবাব দেওয়ার জন্য,0,politics
নুরুর পাছায় গরম ডিম দেওয়া হোক।,0,politics
ধন্যবাদ ভাই সবার চোখ খুলে দিলেন,0,politics
জনগনের টাকা এরকমি বাভে নেয়,0,politics
ভাই এক কথায় সেরা হইছে😂😂😂,0,politics
হা হা হা বাংলাদেশের নেতা তাও সরকারি দলের,0,politics
ভালো লাগলো ভাই আপনার কথা গুলো ❤,0,politics
ট্রাফিক পুলিশের ডিউটি ট্রাফিক পুলিশ কে করতে দেন আপনার এত মাস্টারি করার দরকার নাই মানুষ সবকিছু বোঝে মানুষ এখন অচোদুনা,0,politics
কাউয়া কা কা কা,0,politics
কাদিরা হাগল,0,politics
আপনাকে ধন্যবাদ।,0,politics
চোরের দেশে বাংলা দেশ,0,politics
অপুতো শৃঙ্খলিত ভাষায় কথাই বলতে পারেনা ওকে এখানে এনেছে কেন।তাছাড়া মহিলাতো বেয়াদব আচারনে কথা বলে।কথা বলার সময় এতো তো তো করাতো ভাষা জ্ঞানে অজ্ঞতার প্রমান। তাছাড়া কথা বলা ক্ষেত্রে ভদ্রতা বজায় রেখে কথা বলতে জানেনা। উনার মত একজন অভদ্র মহিলা এখানে এসে কথা বলার যোগ্যতা রাখে না। ওনার কথা বলার যোগ্য স্থান হচ্ছে গ্রামের ঝগড়াটে মহিলাদের সমাজে।,0,politics
ইলিয়াস সাহেবের সাথে গোলমাল করার জন্য আপনার ভিডিও দেখা বন্ধ করেছিলাম,0,politics
এটা আসলে কিছুই না ভাই এটা হল কিয়ামতের এক আলামত,0,politics
ইনু কাহু খালি শেখ হাছিনা শেখ হাছিনা করেন কেন???,0,politics
আপনার তুলনা আপনি নিজেই ভাই✊✊,0,politics
আওয়ামীলীগ যে কতটা ছ্যচড়া তা এই অলোচনা থেকে আবারও বোঝা গেল।,0,politics
ভাইয়ের ভিডিও গুলা অনেক ভালো লাগে😍 যারা ভাইয়ের চ্যানেল টা সাবস্ক্রাইব করছো প্লিজ আমার চ্যানেল টা সাবস্ক্রাইব করে আমাকে একটু সাপোর্ট করো আমার চ্যানেলের ভিডিওগুলা ভালো লাগবে ইনশাআল্লাহ।,0,politics
সত্যি একদিন প্রকাশ পাবেই,0,politics
ধন্যবাদ দিদি কথা গোলা গুলা করে বুজিয়ে দিন জয় বাংলা জয় হোক বাংলার মেহনতী মানুষদের জয় হোক নৌকার জয় কয়েছ,0,politics
অপু উকিলের মুখ দেখলেই গা জ্বলে!!,0,politics
কাদিরা ফুরাই হাগল অই গেচে। গরমের মইধ্যে হেতে কোট গাত দিই আডে।,0,politics
কমেন্ট পডে মজা পাইছি।।জনগন কার পক্ষে দেখতে হলে কমেন্ট পড়ুন।,0,politics
স্যারের পেটটা আগের চেয়ে একটু বেরেছে।,0,politics
অভিনয় টা সুন্দর ছিল,0,politics
আগামীতে ট্রাফিকের কাজ করা লাগবে এখন ট্র্রাই চলছে,0,politics
তে সালায় একটা পাপি স্যার,0,politics
আমি আঁচি তোমার সাথে,0,politics
ওবায়দুল কাদেরের সাথে একটি প্রাণী তুলনা হয়। সেটি কাক,0,politics
কার সাথে কি পান্তা ভাতে ঘী। কোথায় কাদের আর কোথায় বেগম জিয়া।। এ যেন শৈবাল এর সাথে কমল কাননের তুলনা।,0,politics
দুই দিনের বৈরাগী ভাতে রে বলে অন্ন।।,0,politics
মানুষ হাসতে হাসতে পাগল হলো কারন খালেদা জিয়া আর কাদের খালেদা জিয়া মানুষের জন্য জেলে আর কাদের কি করে,0,politics
প্রধান মন্ত্রীকে তার জায়গা থেকে সরিয়ে নুর ভাইকে দিয়ে বাংলার মাটিতে সঠিক বিচার পাবে সবাই আইন মতো চলবে সব কিছু ভাইয়া এগিয়ে যান আল্লাহ আপনার সহায় হক,0,politics
জাতিয় ভাবে ব্যংক ডাকাত হলো শেখ পরিবার শেখ কামাল যা টেলিবিশনেও প্রচার করা হয়েছে,0,politics
কাউকা বিদাই।,0,politics
শিবির নয় ছাত্র রাজনীতির বিষবৃক্ষ হলো ছাত্রলীগ।,0,politics
আপনি রাজনীতি না করে টিভি অভিনেতা হলে অস্কার বিজয়ী হতেন। আর কত অভিনয় করবেন। আপনি একা গেলেন কেন। বাকি ছাত্র সংসদের সদস্যরা ছাড়া,0,politics
আমারা চাই শেখ হাসিনার পরিবর্তন,0,politics
অপু উকিলের জ্ঞান এবং বুদ্ধির অভাব,0,politics
ওবায়দুল কাদের আগে জানতাম ওনি তরুণী নারী রমণীর কাছে অনেক জনপ্রিয় নেতা। এখন জানলাম ওনি ঘড়ির কাছে জনপ্রিয়। ঘড়ি বনাম তরুণী ওবায়দুল কাদের,0,politics
ভাই আপনাকে এখন এতো কম কেন দেখি। আল্লাহ আপার পথ চলাকে আরো বেগমান করুন। সত্যের পথে সবসময় দেখতে চাই।,0,politics
নুরু ভাই আপনি সঠিক,0,politics
ওবায়দুল কাদেরের চেয়েও নিচে,0,politics
তোমাকে পিঠানো দরকার।কারন তুমি একজন মিথ্যুক,0,politics
তাকে বলে বি বাড়িয়ার সাহসী মেয়ে যে কাউকে পরোও করেনা,0,politics
ভালো ভালো মেয়ে পাউয়া যাই নাকি,0,politics
এতদিন যে এম পি মন্ত্রিদের গাড়ির লাইন্সেস ছিলনা তা কি তিনি দেখেন নাই।,0,politics
গনতন্ত্রের জন্য একমাত্র মানুষ খালেদা জিয়া আর কাউয়া কাদের ভোট চোরাই সরকারের মন্ত্রী। তুলনার কথা কেন আসছে?,0,politics
কাউয়া বলছে এটা তো খুব সুন্দর কথা বলছে সে তো কাউয়ার চেয়ে ও খারাপ,0,politics
হাহা রিয়েক্ট কোথায়,0,politics
এই মহিলা পাগল নাকি আমি ভোটার হওয়ার পর থেকে ভোট দিতে পারছিনা আওয়ামীলীগ নিজেরাই রাতে সিল মেরে সব ভোট শেষ করছে।মানষতো এখন আর ভোট দিতে যায়না। যে জন যায় তাও আওমীলীগ লোকেরা ভোট দিতে দেয়না বলে বাড়ি যান ভোট হয়ে গেছে। এর আগে কখনওতো এমন হয়নি।।আমাদের এলাকায় বিনপির দূর্গ বলে সেখানেও আওমীলীগ জোর করে ভোট নিল এখন সাধারন মানুষ সবই জানে আওয়ামীলীগ তো এ সৈরাশাসকে চ্যাম্পিয়ন,0,politics
এটা কি বাংলাদেশ সাসন এটা কি সাদিন দেশ,0,politics
ভালো হয়েছে খুশি হয়েছি কলা ঠিকমত কথাই বলতে পারেনা তারে এত বড় পদে দিয়ে রাখছে সবচেয়ে ভালো হয় একজন চালু মানুষকে দিতে হবে যাতে সে ভালো বক্তব্য দিতে পারে,0,politics
আওয়ামিলীগ সরকার ইনু কে মন্রিসভা থেকে বাহিরে রাখে উত্তম কাজ করেছে।,0,politics
আশলে নুর কাদের এজেন্ডা বাস্ত বাওয়ন করতে চাইছে শেইটা তজন্ত করে দেখা উচিদ নুর তথা গতিত নুরের অনুসারিরাইজে সবকিছু বুজেন তাতো হতেপারেনা দেশের জনগনকে বোকা বানিয়ে নুর তার সাংগো পাংগোদের নিয়ে জাইচ্ছে তাই করেজাবে তাতো দেশের জনগন মেনেনিতে পারেনা ঢাকা ইউনোবারছিটিতেতো আরো মানুষ পড়াশোনা করেছেন নুরজে সবার চাইতে বেশি বোজেন তাকিঠিক আর ভিসির উপরে ও তার বাসায় জে হামলা করেছিল তারিবা কিবিচার করেছেন সরকার কোঠা আন্দলনের নামে জেই নইরাজ্জা ছিস্টি করেছেন তাতেতো মুক্তিযুদ্ধাদের অপমান সহ দেশের সাধিনতাকে অশিকার করাহয়েছে আর জারা দেশের সাধিনতাকে অশিকার করলো তাদের জদি বিচারকরানাহয় তাহলে দেশ ও দেশের সাধারন মানুষের অধিকার হুমকির মোখেপরবে এটা সরকারের ভেবে দেখা উচিত অতি গুরত্ত সহকারে।,0,politics
আই সেলোট নুর ভাই,0,politics
অনেক ভালো হয়েছে,0,politics
কা কা,0,politics
দেশে রকমের কিসের জন্য হইতেছে আল্লাহ,0,politics
আওয়ামীলীগ বলতে জারক,0,politics
শালা কাউয়া না তো কী???,0,politics
আল্লাহ বিচার করবে,0,politics
কাদের সাহেব যেখানে মহিলা আছে সেখানে যান নাকি মহিলারা কাদের সাহেব যেখানে থাকেন সেখানে ছুটে আসেন?কোনটা ঠিক?,0,politics
এই কারনে আমাদের রাস্তায় রট না দিয়ে বাঁস দেয়,0,politics
আমি ওবায়দুল কাদের স্যারকে ধন্যবাদ জানাই এই ধরনের পরিচালনা জন্যে কারন এই ভাবে এম পি মন্ত্রীরা নিজ নিজ দায়েত্তে কাজ করলে বাংলাদেশ জনগম আওয়ামীলীগের আর ছাত্র লীগের যুবলীগের কথা বা দলের কথা সারাজীবন মনে থাকবে এবং মাননীয় প্রধান মন্ত্রী শেখ হাসিনার কথায় দেশ এগিয়ে যাচ্ছে এগিয়ে যাবে বাংলাদেশে সরকারি সব জায়গাতেই দুর্নীতির আর দুনীতি,0,politics
স্যার আপনাকে কি ভিপি নূর ফোন দিয়েছিলো? স্যার না দেয়নি। মিথ্যা বলেন কেনো? আমার সামনে আপনাকে ফোন দিয়েছিলো!!! স্যার নূর? হ্যা দিয়েছিলো। 😡😡😡😡 মিথ্যাবাদী শিক্ষক,0,politics
বেগম জিয়া কোন দিন ভোট চোরি করে ক্ষমতায় আসে না তোমার আওয়ামীলীগের মত বিগম জিশা সম্মানের মানুস সম্মান নিয়ে থাকবে সারা জীবন এখন মানুস আওয়ামীলীগকে ঘৃণা করে আবার আসছ বড় বড় কথা বলছে একবার শুধু নিরপক্ষ নিরদলিয় প্রসাশন ছাড়া একটা নির্বাচন দিয়ে দেখ তোমাদের কি জবাজ দিয় বাংলার জনগন,0,politics
ওকে মন্ত্রী না করে আওয়ালীগ ভালো কাজ করেছে,0,politics
হায়রে আলু!!😢,0,politics
কি বলবো বলার ত কোন ভাষাই খুজে পাইনা।,0,politics
দুইটার একটাও ভালো না। আওয়ামী লীগ বিএনপি দুইটাই ভন্ড,0,politics
সবার উচিত নুর ভাইকে নিরাপদ রাখা। যেভাবে রেখেছিল মুজিব কে।,0,politics
একটা ঘড়ির টাকা দিয়ে কতটা পরিবার চলতে পারত। সবগুলো চোরের গোস্টি দেশটারে লুটকরে খায়তাছে,0,politics
মিথ্যা বলে নুরুল,0,politics
ধিক্কার জানাই এ সমস্ত নোংরা রাজনিতী কে,0,politics
দেশের জনগনের টাকা তাদের হাতে পকেটা ব্যাংকে বাড়িতে।,0,politics
হা হা হা হা হি হি হি হি হু হু হু হু,0,politics
আমাগো ওবায়দুল কাদের এতো মিথ্যা বলে সেটা নোয়াখালীর মানুষ জানে হেতের শরীলে আতর লাগিয়ে গুরে কিন্তু হেতের পকেটে গাঁজার হুরিয়া থাকে।,0,politics
মাননীয় বলেননি শেখ হাছিনা বলার পূর্বে। ইনু কথায় যথেষ্ট ইতরামির দুর্গন্ধ বেরুচ্ছে। ইনু যেকোন সময় পল্টি মারতে পারে। তোর মত ইনুকে মাত্র এক গ্লাস পানিতে মিশিয়ে ফেলা যায় বেয়াদব একটা। আওয়ামীলীগ ছাড়া কোন খাওয়া নাই ইনুর। হায় হায়!!!!!,0,politics
আগে জানতাম কাদের সাহেবের শুধু মেয়েদের কালেকশন আছে !!!এখন দেখি ঘড়িরও কালেকশন!!!! জয় বাংলা!!!! কাদের সাহেবকে সামলা!!,0,politics
একটা ছেলের উপর বার বার হামলা হচ্ছে বলার পরেও কোন আইনের ব্যবস্থা দেওয়া হচ্ছে না কেন।,0,politics
এ হলো আমাদের স্বাধীন বাংলাদেশের মন্ত্রীর ব্যবহার বিআরটিসি স্টাফ যে কিনা মন্ত্রীর চেয়ে বেশি কষ্ট করে খেটে খায় তাকে তুই বলে সম্বোধন করেছেন আমাদের মন্ত্রী বাহ জয় বাংলা,0,politics
এরা নিজেদের ভাবেটা কি এভাবে কি এ সমস্যার সমাধান করা আদৌ সম্ভব?? আরে নাটকলীগেরা আমার থেকে আইডিয়া নে😎,0,politics
ওবায়দুল কে সরাসরি জুতা মারা হয়েছে,0,politics
খোঁজ নিয়ে দেখো ক্যাসিনো সম্রাট উনার হাত আছে কেসিনোর এর সদস্যরা তাকে সব উপহার দিয়েছে কেউ গালাগালি করবেন না সিরিয়ালে দাঁড়ান সবাইকে সুযোগ করে দেওয়া হবে গালাগালি করার জন্য 👍👍👍,0,politics
বাংলাদেশের প্রান বেগম খালেদা জিয়া।,0,politics
ছোট ছোট পুলাপাইনও কাউয়া মন্ত্রী কয় ভাল মার্কেট পাইছে ব্যাটা,0,politics
কাদেরকে যেন সাধারণ সম্পাদক না দেওয়া হয়,0,politics
রূমিন আপুকে বললাম এগিয়ে যেতে। আপনার বক্তব্য অসাধারণ,0,politics
উনাকে তো আগে পরিস্থিতিটা বুঝতে হবে। উনি তো দুধের শিশু! মাত্রই পয়দা হলেন! এই লোক শিক্ষক?!!! এ কি পড়াবে ছাত্রদের? প্রাচ্যের অক্সফোর্ডকে এরা বস্তি বানিয়ে ফেলেছে এখন।,0,politics
হাহাহাহাহা,0,politics
এজন্যই তো বলি মরার ঘর থেকে উঠে এসেও রাজনীতি ছাড়ে না ক্যা!,0,politics
আওয়ামী লীগ এবং বিএনপি একই মুদ্রার এপিঠ ওপিঠ।,0,politics
ধন্যবাদ ভাই অপনাকে। আসলে আন্দলোন ছারা আমরা কিছু করতে পারি না এখন তাই আময়দের এ অবস্তা তাই তারাও ভাবে এটাই কিছু দুই চার দিন পর সব ভুলে যাবে,0,politics
খাওয়া দাওয়া শেসে কিন্তু কাদেরকে ভুলে যেওনা রাত্রেও দেখা হবে,0,politics
ভাই কি বলুন চুরি বিদ্যা বড় বিদ্যা যদি না পড়ে ধরা এবার তুমি খাইছো ধরা ভালো থাকবেন ধন্যবাদ,0,politics
সোহেল তাজ কে সাধারণ সম্পাদক পদে দেখতে চাই।,0,politics
কাউয়া তো কাউয়াই হালা কাদের,0,politics
আপু এটা আমার লেখা না এটা বেয়াদব এর জন্ম হয়েছে বেয়াদব যে মহিলা রাস্তায় ছুড়ে মারে তার মত বেয়াদব আর দুনিয়াতে নাই,0,politics
দেশটাকে আমরা আর রক্ষা করতে পারলাম না। আমরা লজ্জিত বাংলা মা,0,politics
সাহেদ ভাই খুব সুন্দর আলচোনা করেছেন।,0,politics
ফালতু,0,politics
এটা নিশ্চিত জামাত শিবিরের যড়যন্ত্র,0,politics
যেই দলের নেতা জনগণের অধিকার কাইরা নেই ভোট চুরি করে সেই দলের কেউ বেগম জিয়ার সমান হবে না,0,politics
ঠিক,0,politics
আলোচনায় কোন তথ্য নাই শুধু ভুয়া আলোচনা।,0,politics
গত বছরে আওয়ামিলীগের অনেক নেতাই টাকার পাহাড় বানিয়েছে বিভিন্ন ভাবে। ওবায়দুল কাদের এত বড় মন্ত্রী এবং দলের সাধারন সম্পাদক হয়েও এত টাকা বানায় নি যে সেটাই অনেক। কি বালছাল ঘড়ি নিয়া বিশ্লেষন করেন? পারলে টেন্ডার বা অন্য টাইপের কিছু নিয়া আলোচনা করেন। এত বড় নেতা হলে দামি ঘড়ি গিফট করবেই উনার সিঙ্গাপুরের চিকিৎসা খরচ উনি বহন করে নি ইভেন প্রাথমিক কিছু খরচ করলে রাষ্ট্রও এত বহন করে নি। বড় বড় নেতা হলে তাদের খরচ চালানো অভাব পড়ে না। এসব চুলের ঘড়ি বাদ দিয়ে বড় সিরিয়াস ইস্যু নিয়ে কথা বলেন।,0,politics
দুধ গুলি ডাকেনা কেনো ?,0,politics
তাহারা দূর্নীতিতে বার চাম্পিয়ন ট্রফি অজ দেয়ার,0,politics
অনেক দিনের শখ ভালো একটি ঘড়ি পরবো। কিন্তু সামর্থ নেই বলে এখনো পরা হচ্ছে না। ইনশাআল্লাহ একদিন ।।,0,politics
শিক্ষা আনগনে রাজনৈতিক নামক ভাইরাস ঢুকিয়ে দেওয়া হয়েছে। ধংশ হওয়া সময়ের বেপার।,0,politics
আমরা সবাই খুশি,0,politics
কাত্তার বাচ্চাদের জন্য দেশটাই শেষ🤬🤬,0,politics
তেল অনেক দিয়েছেন আর না আর না ।,0,politics
এই ঘড়িগুলোর সবগুলোই রেপ্লিকা পাওয়া যায় ।,0,politics
যেমন প্রধানমন্ত্রী তেমন তার চেলাপেলা !,0,politics
ইনু তোমারে আর তুদবেনা আমুলীগ। রাজাকার তসবির দানা গুনতে গুনতে কবরে যাবা তারপর আসল খেলা দেখবি।,0,politics
ভাই আপনি যে ভাবে বললেন। মনে হচ্ছে তার সম্পদ সব আপনার কাছে জমা। আপনি একটা ফালতু ইউটিউবারা,0,politics
হে,0,politics
নুর বাইয়ের মা নুরবাইকে আরাইবসরের বয়স রেখে মারাজায় তাই সকল মাদেরকেবলবো মায়ের বালবাসাদিয়ে নুর বাইয়ের উপরযে হামলা হইয়াছ তার বিচার চান,0,politics
আওয়ামিলীগ দলের উচিত এসব নেতাদের সাথে জোট না করে শুধু এরশাদ সাহেব এর ধরে রাখা উচিত।বাকি সব বাদ দেওয়া উচিৎ,0,politics
ইউটিউবের বদৌলতে আমাদের দেশে এখন উপস্থাপকের ছড়াছড়ি । তাদের কিছু কিছু বাংলা উচ্চারন সুনে রীতিমত ভায় লাগে । যাক আপনি সত্যি একজন উচ্চমানের উপথাপক আপনাদের মতো মানুষের কাছে আমাদের মতো হত দরিদ্র মানুষের অনেক আশা যখন দেশ ভয়াবহ দুর্নীতির মহা সমুদ্রে নিমজ্জিত ।,0,politics
সরকারের পালক পুত্র এরা কিছুই হবে না।,0,politics
তুই ইনু আর মেনন যদি হাসিনার হাত না দরতি তা হলে জীবনে এমপি ও হতে পারতিনা । আবার মন্ত্রী ।,0,politics
সহমত।,0,politics
এই ঐক্য না থাকলে আবার জঙ্গি মাথা চারা দিয়ে উঠবে!,0,politics
ছারেরে আগে পিটাও সবাইমিলে সব বালহবে,0,politics
বাংলাদেশের রাজনীতিকে,0,politics
এ লাইসেন গুলা অনলাইনে দেকেন তাহলে বুজবেন আসল নাকি নকল,0,politics
কমেন্ট পরলেই বুঝবেন কাকে জনগন বেশি ভালো বাসে।,0,politics
ভাল লাগেছে,0,politics
আমি অপু উকিলকে বলছি ছোট মুখে বড় কথা মানায় না বুঝছেন অপু আপা,0,politics
কিছুই বলবো না।আল্লাহ বিচার করবে,0,politics
ভিডিও পরে দেখবো আগে কমেন্ট করব ফাস্ট কমেন্ট শুধু আপনার ভিডিওর অপেক্ষায় থাকি ভাইয়া,0,politics
ভাই ভিডিও বানাইতে এতো দেরি হয় কেন???,0,politics
ওনাকে৷ কথই জেনুদেকেছি আগে,0,politics
কুতারা,0,politics
মনে হয় অাসল না ঝিন ঝিরার মাল।,0,politics
এই দুনিয়াতে দুই দিনের বাহাদুরি চোরের বাচারা,0,politics
রাইট কথা খালেদা জিয়ার উপর গজব পড়ুক,0,politics
ঢাবি কি শিক্ষালয নাকি রাজনিতীর কারখানা,0,politics
হিন্দু মহিলাটা বেশি কথা বলে,0,politics
ধন্যবাদ প্রধানমন্ত্রীকে ইনু ও মেননকে মন্ত্রীত্ব না দেওয়াতে,0,politics
এই হল গরিব দেশের গরিব জনগণের ট্যাক্সের পয়সায় শালা বিশ্ববিদ্যালয়ের শিক্ষার হালচাল। গণতন্ত্রের নামে ক্যাডার তন্ত্র এবং ব্যক্তিতন্ত্র।,0,politics
সকাল গনতন্ত্র মানুষ কে বলবো। গনপজাতন্ত্রী বাংলাদেশ। এর মানে কি। জনগন দেশের মালিক। হাসিনার সরকার টিকে আছে শুধু রাষ্ট্রের হাতে গনা জন মানুষ এর কারনে। রাষ্ট্রপ্রতি সুপ্রীম কোর্টের প্রধান বিচারপতি নির্বাচন কমিশন সেনা বাহিনীর প্রধান পুলিশ বাহিনীর প্রধান রেব বাহিনীর প্রধান। বি জে বি এর প্রধান আর বাকি জন রাষ্ট্রের কিছু বেইমান নিজেকে অনেক জ্ঞানী মনে করে। ও ভারত কে বন্ধু ও ভাই মনে করে। রাষ্ট্রের এই জন মিরজাপর কে মেরে ফেলো বা কৌশল করে গুম করে দাও। তার পর দেশ হবে নিরপেক্ষ। হে সাধীন রাষ্ট্রের সাধীন মানুষ। তবেই লাখ শহীদের আত্মা সানতি পাবে। তার পর জনগন তার মালিকানা ফিরে পাবে। তার পর দেখবে ভারতের দালাল রা সাবধান থাকবে। আমি কোন দল করি না। আমি দেশের মালিকানা ফিরে পেতে চাই। এটা অনেকে মনে করেন বিষয়টি রাজতন্ত্র। আমি বলতে চাই লাক শহীদ কেন দেশের জন্য জীবন দিলো। গণতন্ত্রের জন্য। যুদ্ধের সময় শেখ মুজিব পরিবারের কেউ দেশের স্বাধীনতার জন্য জীবন দেই নাই। সেই তারা আজ কি করে  মানুষের ভোট অধিকার ও গনতন্ত্র মানে বুঝবে। বাংলার সাধীন মানুষ তোমাদের বিবেকের কাছে প্রশ্ন।,0,politics
এ সরকার কি অরাজগতা শুরু করছে কি ভাবে মানুষ বেঁচে থাকবে বুঝিনা যতিদন যায় ততই খুনখারাপি বেড়ে যাচ্ছে,0,politics
চার কি করবো মিথ্যা না বইলা চার জানে চার সত্য বল্লেযে চার ই গায়েব হইয়া যাইবো আমাদের দেশের পরিস্থিতি টাই এমন হয়ে গেছে,0,politics
ভাই সব মন্এী চোর এটা তো জানা কথা।,0,politics
কোথায় বেগম জিয়া আর কোথায় কাদের,0,politics
খুব সুুন্দর ভিডিও,0,politics
আল্লাহর কাছে কিভাবে হিসাব দিবে ঐটা আল্লায় জানে,0,politics
এরা ডিএনএ টেস্ট করে সন্ত্রাসীদের দলে নেয়। ছাত্রলীগ যার প্রমান। যাদের শেখ হাসিনা নিজে ডিএনএ টেস্ট করে সিলেক্ট করছিল পরে দেখা গেল তারা চাঁদাবাজ!!!!,0,politics
আওয়ামীলীগের এই প্রতিনিধি পাগল তাকে পাগলা গারদে পাঠান,0,politics
আপনার মা কই এখন বাবা??,0,politics
কউয়াকে দুইটা পাখা দেওয়া দরকার সে যেন গন গন সিংগাপুর যাইতে পারে। কা কা।,0,politics
চোরের দল মরার পরে আল্লাহ এদের চরম শিক্ষা দিবেন ইনশা আল্লাহ,0,politics
ভালো লাগলো ভাই 🌹 সুন্দর কাদের কাকা 😎,0,politics
দেশ সেরা বিশ্ববিদ্যালয়ে পড়ে অথচ একটাও সুশিক্ষায় শিক্ষিত হয়নাই। যত্তসব,0,politics
মানুষ ও আদিখিলা কমনা,0,politics
ট্যাংকের উপর লাফানো¡!!!!!!!!!!!!!?,0,politics
চোর যখন মহা তারকা তখন দেশের পরিস্থিতির উন্নতি হওয়া অসম্ভব।,0,politics
এতো কারাপ কাজে লিওতো মানুশ ওদের বিরোদে মামলা হামলা গোলি বুলেট ইওজ করেনা কেন বাংলাদেশের আইনের লোক জন ও পুলিশ সরকার এই বেপারে কি বিচার হবেনা জতো শব মামলা হামলা বিএনপি জামাতি ইশলামের ওপরে মামলায় আর হমলা শতো কতায় বলেই জংঘি বাদি হয় শারা বিশ্ব মুশলিম গন তাই না বুজি,0,politics
আমাদের টাকা তাদের বিলাসিতা।,0,politics
এবা জদি হাসিনা তার বাবার বিচার করে তা হলে ইনুুর ফাশি হবে,0,politics
কাদের সাহেব আর কত পাগলামি করবেন।এসব করার কিদরকার মানুষ সব বুঝে,0,politics
ফাইন রুমিন আপা।,0,politics
মানলাম তাকে গিফট দিছে কিন্তু সে এত বড় নেতা তার কি বুঝা উচিত না কেন এত দামি জিনিস দিচ্ছে,0,politics
আমাদের ছাএ লীগ কি করে একটা গুলি করে মেরে ফেলবে চলে,0,politics
স্যার কি এত বছর দেশের বাইরে ছিলেন !!!!!,0,politics
রাজনিতিবিদ রা জানে মারা গেলে খবর খারাপ আছে তাই এই খানেই বেহেশত এর একটু সুখ অনুভব করতেছে। করুক সময় শেষ হলে বুজবে,0,politics
অপু উকিল একটু বেশি বুঝে।,0,politics
কথা ঠিক ওবায়দুল কাদের এর সাথে বেগম জিয়ার কোন তুলনা হইতে পারেনা কারন ওবায়দুল কাদের এর সাটিফিক্সড গুলো বেগম জিয়ার নেওয়ার কোন খমতা নাই।,0,politics
বাংলার হিরো,0,politics
ভাই আপনার কথার সাউন্ড আরো স্পষ্ট করা দরকার আর ব্যাকগ্রাউন্ড মিউজিক কম করা দরকার। এমন কিছু আপনার থেকে আশা করিনি।,0,politics
লাভ রিয়েক্ট এর ব্যবস্থা নাই কেন? ভাই তোমাকে পেলে বুকে জরিয়ে ধরবো৷ হাজারও সালাম তোমাকে৷,0,politics
খালেদা জিয়া মুক্তি চাই,0,politics
কাক কি কখন ও ময়ূর হতে পারে 😆😆😆😆😆😆,0,politics
অপু উকিল নিজেও জানে না নিজে কি বলছে তার মুখস্ত করে আসা কথা গুলো বলার আগে জানা উচিৎ ছিল সেটার মধ্যে সব গুলো সত্য কিনা,0,politics
আপনার ভিডিওগুলো ভাল লাগে,0,politics
💟 ভাই তুমার কলিজাটা বহুত বরো ভাল লাগছে 💟,0,politics
ভাই তোমার শরীরের পুরাটাই কলিজা😍,0,politics
এইগুলো দামি ঘড়ি আমি ফহিন্নি টাকার যেই ঘড়ি ব্যবহার করি এর স্টাইল এইসব ঘড়ি থেকে অনেক সুন্দর🤣🤣🤣🤣🤣🤣🤣,0,politics
ভাইয়া আমি টাইম জোন থেকে টাকায় একটা ঘড়ি কিনেছিলাম। খুব শখ করে বিয়ে উপলক্ষে জমানো টাকা দিয়ে কিনেছিলাম। কিন্তু ঘড়িটা মাস ও ব্যাবহার করতে পারিনি। বিস্তারিত এখানে বলছিনা টাইম জোন এই নকল ঘড়িটির ব্যাপারে কোনো হেল্প ই আমাকে করেনি আপনি কি এই ব্যাপারে কোনো হেল্প করতে পারেন?,0,politics
আল্লাহ তুমি সাহায্য কর,0,politics
অপুর মতো নষ্টা মহিলার কথায় জনগণের কিছু যায় আসে না ।,0,politics
হলের ভিতর কি ডিম বেচে ভাই। আগের পরিকল্পনা,0,politics
তোরে সামনে পাইলে জুতা দিয়ে এমন মারা মারবো,0,politics
উন্নয়ন উন্নয়ন উন্নয়ন।,0,politics
একজন সত নিরবাচিত ভিপি সেও আজ আওয়ামি সন্ত্রাসির হাততেকে নিরাপদ নয়,0,politics
আপনাকে এই ধরণের রিপোর্টেই ভাল লাগে। বিতর্কিত ইস্যু গলো এড়িয়ে চলাই শ্রেয়। ধন্যবাদ,0,politics
ভাই কিছু বলবো কি,0,politics
অপুর কথা বলছেন কই কোথায়ও তো অপু আপু নেই ফালতু,0,politics
কোথায় গু খাওয়া কাউয়া আর কোথায় খালেদা জিয়া।,0,politics
অপু উকিল কয় পয়সার রাজনীতিবিদ সেটা আমার প্রশ্ন নয়।আমি বিএনপি করি বলে অন্ধের মত তারেক জিয়াকে নিষ্কলুষ দাবি ও করতে পারিনা। আওয়ামী লীগের জন্ম স্বাধীনতার আগে তারা স্বাধীনতার চেতনায় গণতন্ত্রের জন্য সুশাসনের জন্য নিজেদের জীবন উৎসর্গী ত্যাগী নেতা হিসেবে দাবী আওয়ামী নেতাদের। তাদের ভাষ্যমতে বিএনপির সাথে তাদের তুলনা অযৌক্তিক। কিন্তু থেকে একেমন সুশাসন গণতন্ত্র এবং স্বাধীনতার চেতনায় উজ্জীবিত তথাকথিত আওয়ামী লীগাররা!দূর্ণীতি আর দুঃশাসনের জবাব এই বাংলার মাটিতেই দিতে হবে আওয়ামীলিগারদের। সালের পর সর্বজন স্বীকৃত অবৈধ এই শাসনকালের প্রতিটি খুন গুম দূর্ণীতির পাই পাই করে শোধ দিতে হবে আওয়ামীলিগারদের।এই দেশকে ভারতের তাবেদার রাষ্ট্রে পরিণত করার ভয়ানক পরিণতির শিকার বাংলার জনগণ পাই পাই করে শোধ নেবে আওয়ামিলীগারদের উপর। ইতিহাস থেকে শিক্ষা নোওয়া আছে সব রকম শাসনামলের হিসাব দুনিয়ায় ই আল্লাহতালা কিছু টা নজির দেখান।,0,politics
আর কতো খাইবি দেশটাকে লুট করে,0,politics
সোনলে তোমার মারে করবে,0,politics
অসৎ নেতাদের কে দয়া সরে দেন।,0,politics
মজাই মজা,0,politics
কেন জানি এগুলারে দেখতে মন চায় না,0,politics
এগুলা করে রাস্তায় আরো জানজট সৃস্টি করা,0,politics
ভাই কোন কাদেরে কথা হচ্ছে এখানে চৌরাস্তা চায়ের দোকানদার কাদের না কি কাউয়া কাদের ? !!,0,politics
এসব ছাত্রলীগের সব গুলারে কুবা,0,politics
ঠিক কথা,0,politics
ধন্যবাদ আপনার বানানে ভুল বোঝাবুঝি খেয়াল করুন জয় বাংলা জয় হোক এই বাংলার মেহনতী মানুষদের জয় হোক নৌকার,0,politics
একটা বাগের বাচ্ছা নুর,0,politics
আজ আওয়ামী লীগ ক্ষমতায় থাকায় এই আজাইরা নিউজ করতেসে বি এন পির ক্ষমতার সময় নেতাদের সম্পদের হিসাব করে দেখেন,0,politics
জয়কে নিয়ে আসা হউক।,0,politics
আরে হ্লা সবগুলোর রেপ্লিকা স্যাম টু স্যাম বেশি হলে দশ হাজার টাকা! যাচাই না করে আন্দাজেই প্যাচাল পারে!,0,politics
অ ভাই আমি এম পি মোস্তাফিজ রহমান এর এলাকা বাঁশখালী লোক 😮,0,politics
সন্ত্রাসী ছাত্রলীগ না নূরুর দল।,0,politics
অপু অামি হিন্দু কিন্ত তোর মতো পাগল না অারে তুইত হলি অাওয়ামীলীগের চামচা তোকে বলতে চাই কাদের তো দূরে থাক মজিবর ও খালেদার জিয়ার কাছে কিছু না,0,politics
তাসিনেশন বিদেশে থেকে আওয়ামী লীগের বিরুদ্ধে কথা বলতে প্যান্ট ভিজে যায় আর তুমি দেশে বসেই বীর এর মত সাহস। সাবাস। এগিয়ে যাও বন্ধু।,0,politics
নূরা নিজের স্বার্থের লাইগা সাধারণ ছাত্র ছাত্রীদের ঢাল বানিয়ে ব্যবহার করছে একদিকে নিজেরে ভিপি মানে অন্যদিকে আবার ডাকসু নির্বাচন চায়।,0,politics
যারা ছাত্রলীগ করে তাদের থেকে নিকৃষ্ট প্রানী বলতে আর কিছু নাই,0,politics
এই সব ডিম লীগ এদেরকে না বলুন।,0,politics
কাদের,0,politics
কবে জে এই গর্দব গুলো ভুজবে শেখ হাসিনা বাংলার মানুষ কে বিসাশ করেনা সবাই কে ব্যবহার করে।,0,politics
ভাইয়া সাউন্ডটা আরেকটু স্পষ্ট হলে আরো ভালোভাবে ইনজয় করতে পারতাম 😆😁😁😁,0,politics
মানুষ দেখানে কাজ,0,politics
কমেন্ট পড়ে খুব ভালো লাগলো,0,politics
হাহাহাহা! হালায় পাগল,0,politics
এদের খাওয়া শেষ দেশটাকে এবার নতুন রা এসে কামড়াকামড়ি করবে,0,politics
নুরু যেন কোন ভাবেই ভিপি পদ থেকে সরে না যায়,0,politics
মন্ত্রী মহোদয়ের এত দামি ঘড়ি পড়া মোটেও অযৌক্তিক নয়। সম্ভবত এত দামি ঘড়ির কারণে তার সময় খুব ভালো যাচ্ছে।,0,politics
আমি মনে করি বড়ো দুর্নিতি বায হলো আওয়ামী লীগ,0,politics
ইনুর খবর আছে,0,politics
আসলেই জ্ঞান দানের পাত্রটার তা ধারণ করার ক্ষমতা থাকতে হবে। নতুবা উলু বনে মুক্ত ছড়ানো হবে। যারা আগস্টের ঘটনার মত বিশাল ব্যাপারকে ধামাচাপা দিয়ে দেয়া সম্ভব বলে মনে করে তাদের হাতে আর যাই হোক রাষ্ট্র পরচালনার মত গুরুদায়িত্ব দেয়া আহাম্মকি ছাড়া আর কিছু নয়।,0,politics
এরা হলো মা জননী পোলাপান ছাত্রলীগ,0,politics
চোরেরা চুরির বেগনিয়ে পালাতে পারচে না। বুড়ো হয়ে গেছে তাই। নতুন চোরের সন্দানে নেমেছে হাচিনা। যাতে ধরা না পড়ে।,0,politics
এতিমের টাকা চুুরির নাম খালেদা জুয়া,0,politics
অশেষ ধন্যবাদ ভাই,0,politics
লিক বলতে খারাপ বাই,0,politics
মন্ত্রী মহোদয়ের গাড়ির ডাইভার গাড়িতে বসে ড্রাইভ করছে কিন্তু সে সিটবেল্ট ব্যবহার করছেনা। কিন্তু মন্ত্রী মহোদয় ও সিটবেল্ট ব্যবহার করছে না। নতুন আইন টা কি সবার জন্য না। প্রশ্ন থাকলো জাতির কাছে। ভিডিওটা একটু ভালো করে দেখবেন,0,politics
হাইস্যকর এই আইটেমরে পাইলো কই 🤣😂,0,politics
অবাক,0,politics
অবশেষে কাকুর মুখে নোয়াখালীর ভাষা শুনলাম 🤔🤔🙄🙄,0,politics
সালা সাংবাদিক দালাল কারন আপনি এক জনকে সময় দেন আর এক জনকে কথাবলার সময় দেন না রাজাকার সালা,0,politics
ছুটিয়া বাজ তোমার মগজ ধোলাই মানুষ আর খাই না ।নতুন বোতল পুরানো মদ ঠাল।,0,politics
ঘড়ি কিনার টাকা নাই। মোবাইল এ আমি সময় দেখি,0,politics
ধন্যবাদ আপু,0,politics
কাদের এর সুনামে খাটাস হয়েছে এবার কচ্ছপ হবে,0,politics
দেখি কিছু বলি না ধন্যবাদ,0,politics
সঠিক কথা বলেছেন রুমিন ফারহানা জাজাকাল্লাহ খাইরান শুভকামনা রইল আপনার জন্য অনেক গুরুত্বপূর্ণ বিষয় নিয়ে ভিডিও দেওয়া জন্যে ধন্যবাদ আপনার আপু,0,politics
সড়ক মন্ত্রী লাইসেন্স চেক করবে একা সাথে থাকবে একজন এসআই একজন কনস্টেবল এখানে তো দেখি রামছাগল হাজার,0,politics
চোরের মার বড় গলা যেনি টাকা চুরি করতে পারে সে আবার কিসের বাংলাদেশ তিন বারের প্রধানমন্ত্রী বেগম খালেদা জিয়া মত সরকার বারে বারে দরকার নাই ওবাইদুল কাদেরের বাম পায়ের জুতা যোগ,0,politics
কই কাউরা কাদের কই খালেদা জিয়া কোথাই আগার তলা কোথাই ওগার তলা অপু ত একটা বৈদব,0,politics
বাংলাদেশের আওয়ামীলীগের ব্রেন পাগলে খাইছে।,0,politics
কাদের যদি বাইচা থাকে তাহলে ভবিষ্যতে তার অবস্থা বাবর এর মত হইব।।,0,politics
বলেন ম্যাডাম বলেন,0,politics
সালাম ভাইজান,0,politics
পচা ডিম মারলে আরও ভাল লাগত,0,politics
আমরা আপনার পাশে আছে সত্য বলতে কখনই ভয় করবেন না🙌🙌🙌🙌,0,politics
শাহেদ ভাই তিনি যদি আপনার এই ভিডিও দেখেন তবে খুব হতাশ হবেন এই ভেবে যে আপনি তাঁকে ভাবেন নি 😀❗,0,politics
ভদ্রভাবে পোঙ্গায় বাশ দেওয়ার সচ্ছ উদাহরণ,0,politics
এগিন করি বোট নিবেন বুজি৷ হাগল,0,politics
নূর কে তো দেখলাম না,0,politics
কাউয়ারে বাদ দিলে ই ভালো হবে,0,politics
আমার সোনার বাংলা আমি তোমায় 🤮🤮🤮🤮🤮,0,politics
মাত্র কোটি টাকার ঘড়ি কাদেরের হাতে ডেমরার পাতি নেতা খেতার কাছে যদি কোটি টাকার থাকে কাদেরের কাছে কোটি টাকার ঘরি থাকার কথা কাদের চুর বদমাইশ হলেও মানুষ ভাল।।।,0,politics
ওবাইদুলকাদের ওনিএকটা সম্মানিব্যাকতি ওনারতুলনা দিলাম সুয়রেরসাথে কারন সুয়রেরসাথেমিল আছেঅনার,0,politics
আজে বাজে মহিলা এবং পুরুষ কোথায় থেকে যে আনেন যদি আনতে হয় তাহলে রুমিন ফারহানার মত ভদ্র মানুষ কে ডাকবেন ওকে,0,politics
কিসের সাথে কি পান্তা ভাতে ঘি,0,politics
আমাদের ঘড়ির দাম থেকে টাকা হালায় কি করছে দেশটার গুয়া মারা সারা,0,politics
সমালোচকরা সমলোচনা করবেই ?,0,politics
ইনু তুমি এতো দিন দালালি করে হয়েছো তোমার মতো নাস্তিকদের কারনে আওয়ামীলীগ কে আলেম সমাজ আরচোখে দেখে,0,politics
সাবাস,0,politics
টিক,0,politics
ডিম লীগকে না বলুন।,0,politics
কথায় আছে চুরের মায়ের বড় গলা। কথা যে সত্য তা বিএনপির কিছু মাথামোটাদের ঘেউ ঘেউ শোনলেই বুঝা যায়।,0,politics
যদি নানকরে সাধারণ সম্পাদক দেয় তাহলে ধলস হয়ে যাবে।কাউয়ায় খারাপ না।,0,politics
কাল বৈশাখী জ্বর তো হবে,0,politics
আমার কেনা সবচেয়ে দামি ঘড়ির দাম টাকা।,0,politics
কাদের সাহেব হুমকিমুলক কথা বল্লেন নাকি ইনুকে,0,politics
কৃষিমন্ত্রী সেক্রেটারি হতে পারে,0,politics
শান্ত ভাই আমি আপনার সাথে কথা বলতে চাই আমারে ফোন দিয়েন আমার নাম মমিন জামাল পুর থাকি,0,politics
হাসিনা আপা নিজের পায়ে নিজেই কুড়াল মারছে ।সব কিছুর একটা সীমা আছে । ছাত্র লীগকে নিষিদ্ধ না করলে হাসিনা আপার খবর আছে ।,0,politics
মাশাল্লাহ ধন্য বাদ মন্ত্রী সাহেব,0,politics
সাহস ভাই আপনার,0,politics
প্রিয় শান্তনু ভাই প্রশ্ন কিন্তু আমারও থেকে যায় কেনো লাখ টাকার ঘড়ি গিফট দেয় ?? ভাই আপনি কি ইদানীং ভিডিও কি করেন না নাকি ?,0,politics
ওবায়দুল কাদের বড,0,politics
খুবই লজ্জাজনক বিষয় যেখানে বাঙালিরা দুইবেলা পেট ভরে খেতে পারে না মানুষ শীতে কষ্ট করে ঢাকা শহরে অসংখ্য বস্তি যানজটে অতিষ্ঠ মানুষ দেশে লক্ষ লক্ষ বেকার সেখানে আমাদের দেশের মন্ত্রীরা কোটি টাকার ঘরি পরে ফ্যাশন করে ছি ছি কি আর বলব!!!,0,politics
গায়ের জোড়ে চলছে দেশ দেশ কার মামা জোড় যার তার মামা। নুরুর আছে সাধারণ ছাত্র ওদের আছে সন্ত্রাসী ছাত্র। তোদের নাটক আর ভাল লাগেনা ঢাকা বিশ্বঃ মানে ছাত্র লীগের খামার যেখান থেকে নিয়মিত বেয়াদব উৎপাদন করা হচ্ছে ভবিষ্যত জাতির দক্ষ নেতৃত্ব দানের জন্য। যেমনঃ মতিয়া শামিম বদি ইনু মেনন শাহরিয়ার মামুন গণ। কোয়ালিটি প্রোডাক্ট পাব আমরা।,0,politics
ওয়াদুলকাদের কাওয়ার চেয়ে বেশি খারাপ।,0,politics
ছি ছি,0,politics
এই সমস্যা সমাধান দিবেন কে ? কেউ কার কথা শুনছে না।,0,politics
মাস্টার্স পাস করে মাসে হাজার টাকা যে দেশের মানুষ উপার্জন করতে পারেনা । সে দেশের মন্ত্রীর হাতে কোটি টাকার ঘড়ি!!,0,politics
এটাই হোল শেখ হাসিনার ডিজিটাল বাংলাদেশ!! যাখানে সেখানে খুন কোন বিচার হয় না😪😢😢,0,politics
আচ্ছা আমরা প্রবাসিরা কেন প্রশ্ন করতে পারিনা???,0,politics
ধর্ষন কারী নোয়াখালীর মজনু ওবায়দুল কাদেরের শালা,0,politics
কই আকাশ কই চাঁদ আর কই জমিন।কই খালেদাজিয়া কই ওবায়দুল কাদের।হাসি পায় শুধু। কই রাজ রানি কই দিন মজুরি?খালেদা জিয়ার সাথে কারো সাথে তুলনা হয়না। খালেদা জিয়া কি তা অপু উকিল বুঝবেন না কারন স্বার্থ রাজনিতি করে দেশের জন্য করেনা।সবাই চিনে ক কত জগ্য নেতা।,0,politics
আওয়ামিকুতা এরা,0,politics
এই ঘড়ি উনার না কথা ঠিক এটা জনগণের টাকা চুরি করে কিনছে তাই এই ঘড়ি জনগণের 😂😂,0,politics
তুই এমন নাচানাচি করোছ কেন??,0,politics
ভালো লাগলো ভাইয়া !,0,politics
অন্তত আমার অপর নাম খালেদা জিয়া না বাকি বাংলাদেশের কথা আমি জানি না আর বাংলাদেশের অপর নাম যদি খালেদা জিয়া হয় আমি এই দেশের নাগরিকত্ব চাই না সরি!!,0,politics
কোনো লাভ নেই জনোগণ শেখ হাসিনাকে ছাড়বে না।,0,politics
বুজবি মনা বুজবি কাইল মারবি থাপ্পর পারবি গাইল ছাত্র ভাইরা তোমরা পড়া লিখায় মন দাও নিজের জিবন গড় এসব বালছালের রাজনিতি করে কোন লাভ নাই তোমাদের মাথায় কাঠাল ভেংগে খায় কিছু খানেওয়ালারা তোমরা বুজনা???? বুদ্ধিমানদের জন্য আমার এ কথাগুলো উপকার হবে ইন শাহ আল্লাহ বাংলাদেশে ছাত্র রাজনিতি বন্ধহোক,0,politics
শখের দাম লাখ টাকা আমি একজন ছাত্র হিসেবে টাকার ঘড়ি ব্যবহার করি সেখানে একজন মন্ত্রীর কটি টাকার ঘড়ি ব্যবহার করতেই পারেন৷,0,politics
স্যালুট ভাই 😍😍😍,0,politics
বি এন পি র সাপোর্টার ডিটেক্টেড।,0,politics
অসংখ্য ধন্যবাদ আপনাকে সাহসী ইউটিউবার আপনি। আল্লাহ আপনাকে ভালো রাখুক সুস্থ রাখুক।,0,politics
এদের আর কোন কাজ নাই দেশের উন্নতির জন্য কোন একটা কথা নাই।শুধু বদনাম আর গীবত। এঁদের কারনে আজকে বাংলাদেশের প্রতিটি ঘরে ঘরে হিংসা বিদ্দেস শুরু হচ্ছে আমি যে কমেন্ট করছি তাই আমার কাছে মনে হচ্ছে আমি ফালতু সময় নষ্ট করছি আর এরা সারা দুনিয়া নিয়া বইছে দোনটাই খারাপ এদেরকে বসিয়ে বাংলাদেশের সময় নষ্ট করা হচ্ছে।এক জন বলবে আমার সরকার ভালো আর একজন বলবে আমার সরকার ভালো কন সরকার এসে কি নুম্বা ফালাইছে এখনো বাংলাদেশের এক কনা ও ঠিক হয় নি আরু অনেক কিছু করার আছে,0,politics
চোখের ভ্রু প্লাক করা বাবদ প্রতিদিন কত টাকা খরচ হয় সেটা একটু বলবেন!! মেকআপ বক্স এবং শাড়ির কথা নাইবা বললাম!!😅😅,0,politics
জেই দেশে হলমার্কেটর চারশ কুটি টাকা কিছুইনা আর এই দেশেই দুই কুটি টাকার মামলায় একজন পেসিডেন্টের জেলহয় বেপারটা কুব অদৃিসস মনেহয়,0,politics
আল্লাহ ঠিক করুক সব,0,politics
খালেদা জিয়ার সাথে কখনও কাউয়া কাদেরকে মিলানো যায় না।কোথায় কাউয়া কোথায় নেতৃ,0,politics
ভাই তুমি একটা জিনিস সব সময় সত্যি কথা বলো জন্য এতো ভালো লাগে,0,politics
দেখুন আমি বিএনপি সাপোর্ট করি না। কিন্তু খালেদা জিয়ার সাথে আমাদের নোয়াখালীর ওবায়দুল কাদেরের সাথে তুলনা নিতান্ত বোকামি। এটা পাগল ছাড়া কেউ বলবে না।,0,politics
এক পয়সা দাম নাই তার আবার বড় বড় কথা । ওবায়দূল কাদের সাহেব অবশেষে একটা সত্যি কথা অন্তত বলেছেন । আওয়ামীলীগ ছাড়া নির্বাচন করলে এদের অবস্থা কি হতো তা সবাই জানে,0,politics
আপু ভোট চোরের সাথে কথা বলতে ঘৃনা হয়,0,politics
কই আগর তলা আর কই চোকির তলা,0,politics
আল্লাহ্‌র গজব পরুক ছাএলীগের উপরে।,0,politics
জার মাধায় কাপর নাই তার কোন দাম নাই দুই জনের মধ্যে এক জনের তাও আছে কোটি মানুষ দেখবে,0,politics
আল্লাহ হেফাজত দান করুন নুরু ভাইকে। আমিন।,0,politics
কাউয়া মার হাউয়া অপু তোরে লাগামো,0,politics
🤣🤣আমি শিহোরীত🤣🤣,0,politics
ওবাইদুল কাদের ঠিক বলছেন ইনুর হাওয়া নেই আওয়ামীলীগ চাড়া।,0,politics
অপু আপা সত্যের জন্য আপনাকে দেওয়া যায় আজ পযন্ত আপনার কথার কোন ভিত্তি খুজে পাইনা যাদের কথা শুনলে হাসি পায় আপনি তাদের একজন,0,politics
এইসব শিক্ষিত শিক্ষকদের কে আগে জুতা পিটা করতে হবে,0,politics
বাতিজার পুতে মরেনো,0,politics
ভুয়া সরকার লীগ,0,politics
কাউয়া পদ হারালে ছাত্র লিগের সুন্দরী মেয়েদের কি হবে। রাব্বানী শোভন ভাই কিন্তু খুশি হবে।,0,politics
ভাইয়া আপনি সবসময় তোমার ভিডিওর জন্য অপেক্ষা করি,0,politics
আরে মিথ্যা কথা বলতে গলায় একটু হলে বাজে একদিন মরতে হবে,0,politics
কূথায় খালেদা কাওয়ার তূলনাকরে কারশাথে শবপাগল,0,politics
জানিনা ভাই আপনি ইউটিউবে আর কতদিন থাকবেন কিন্তু আপনার সাহস অনেক,0,politics
শিয়া সম্প্রদায়ের আকীদার সম্পর্কে যাদের জ্ঞান কম তারাই বলে শিয়া সুন্নি ভাই ভাই কোন প্রকার বিভেদ নাই অথচ শিয়ারা আমাদের সাহাবাদের সম্পর্কে ভিন্নমত পোষণ করে গালি পযর্ন্ত দেয়!তারা হযরত আলি কে নবীর চেও বড় মনে করে। ওহি নাকি ভূল করে নবীর কাছে আসছে।,0,politics
ফালতু অপু উকিল,0,politics
ছি ছি এই সব কি,0,politics
বারোশো কর্মী সাতশো ভোট খায় দায় সুদ তার নাম জাসদ আর এই জাসদের ফালতু নেতা হল ইঁদুর ওকে ব্যবহার করা যায় কিন্তু মন্ত্রী বানানো যায় না। ওর স্থান হলো ড্যাসবিনে।,0,politics
ষাড় শুয়ার গুলো কি জঘন্য! 😡,0,politics
সিক্ষা নাকি জাতির মেরুদণ্ড তাহলে এরা কি করে আল্লাহ মাবুদ,0,politics
কাউয়া রে টেনশনে দরে মনে হয়,0,politics
কোথায় বেগম খালেদাজিয়া কোথায় কাদের এখানেও দুর্নীতি করার চিন্তা চলছে নাকি,0,politics
আল্লাহ এই বিচার এক দিন এই দেশের মানুষের হাত দিয়ে করাবেনে সবাই কি বলেন,0,politics
এখন কাদের সাহেব বলবেন এখানে জামায়াত বিএনপির ষড়যন্ত্র জরিত আছে।,0,politics
কোথায় আদি নাতের পার আর কোথায় চলে কের হার ।। কাদের,0,politics
গুড আপ্প,0,politics
কায়া কায়া কায়া,0,politics
অপু আপার সব কথ্যা ঠিক আছে অপু আপাকে ধন্যবাদ তিনি সব সত্য কথ্যা বলেছেন,0,politics
একজন সিরিয়াস মাইন্ডেন মেয়ে চাই বিয়ে করবো প্রেম না ভালো জব করি আশা করি হেপি থাকবেন ।,0,politics
বেগম জিয়ার একটা পশমের সমান হতে পারবে না,0,politics
এতগুলা মানুষ পারেনা কুততালিগের নামটা মুছেফেলতে সেক মজিবরের আমলে এমনছিল,0,politics
আয়ামীলিগ চুদিনা,0,politics
মানুষ কুকুরের চেয়েও খারাপ একটা কুকুর আরেক টা কুবুরকে টুকরা করেনা কিন্তু মানুষ তা করে বেরায়,0,politics
বই লিখে বছরে লক্ষ টাকা কামাই কিন্তু লেখে কখন বই,0,politics
হয়ত জামাতের রাজাকারের নামে নতুন লিশ্ট তা চারা কি লিখবে কাওয়া কাদের,0,politics
আপনাদের মত নেতা আওয়ামীলীগের প্রয়জোন নাই সাড়া দেশে আপনাদের দশটি ভোট নাই জনগন আপনাদের বয়কট করায় আওয়ামীলীগ ও বয়কট করেছেন,0,politics
দুদক কই??,0,politics
আপনার মাকে বলেন। নির্বাচন বিহীন সরকার উৎখাত হলেই শুধু মানুষের স্বাভাবিক অধিকার বজায় থাকবে। আমি হলফ করে বলতে পারি আপনাদরকে তারা কখনই টিকতে দিবেনা।,0,politics
অসহনীয় ।,0,politics
ছাত্রলীগ কে মেরে হল থেকে বের করে দেওয়া হোক,0,politics
কাদের সাথে আমার বাড়ির জাড়ুদারের তুলনা চলে,0,politics
বিচার চাই অনৈতিকতার,0,politics
কাদের সাহেবের ঘড়ি একটা পাইলেই হত। একটা বাড়ী কিনে ফেলতাম। হা হা হা।,0,politics
এইদিন দিননা আরো দিন আছে আল্লাহ জানে আপনার করুন অবস্তা হয়,0,politics
আওয়ামী লীগ ভারতের দালাল,0,politics
অপু উকিল পালটু।,0,politics
ওবায়দুল কাদে ঘড়ি পরেই বাংলাদেশের সকল সম্পদ ফ্যাসনে খরচ করছেন । শেখ হাসিনা এর বিচার করুন।,0,politics
ভাবছিলাম অপু উকিল শিক্ষিত। এখন দেখলাম বিখ্যাত মূর্খ ও বটে।,0,politics
ভাল লেখক!? 🤔🤔,0,politics
ছাএলীগ নিয়ে লাইভ এ ভাল খবর শুনি নাই,0,politics
কালকে আমি লাইফ এ আসবো সকল পরশাসন প্রতি আহবান নির্বাচিত নুরুল হোক কে নিরাপত্তা দিন নুরুল হোক কে মেরেছে অবিলম্বে সাশস্তি দাবি করি।,0,politics
হাগলের দেশে পাগলীর আবিভাব,0,politics
এখন দেখছি গনমাধ্যমের অভাব নাই।।আর ছাত্র আন্দোলনের সময় সালারা কই ছিলি।।,0,politics
আব ইনুজি ধারাপারা।,0,politics
সাবাশ বোন,0,politics
এতো টাকার উৎস জানতে চাইলে কি গণতান্ত্রিক এই দেশে আমার জেইল হবে ফ্রেন্ডস?,0,politics
ওরে চোদন,0,politics
অনেক ভালো লাগলো ধন্যবাদ তোমাকে তুমি ভালো থাকবে মনে রাখবে চোরের মার বড় গলা,0,politics
এইখানে তো কাপেরের কারখানা,0,politics
কোথাই রাজধানী আর কোথাই চো ।,0,politics
খা‌লেদা ছি‌লো আর‌মি ক্যা‌ম্পের রা‌তের রানী,0,politics
হাডা উকিল,0,politics
হা হা হা আমাদের গ্রামে একটা কথা আছে যে বাবা মা ভালো না হলে ছেলে মেরা কিকরে ভালো হবে আমাদের হয়েছে এই অবস্তা নেতামন্ত্রী দের লাইচেন না থাকলে সাধারন মানুষের কি করে থাকবে,0,politics
বাংলাদেশের রাজনীতিতে আওয়ামী লীগ ও বিএনপি দুটি বৃহৎ দল যে দুটি দল প্রত্যক্ষভাবে শেখ হাসিনা ও খালেদা জিয়া নিয়ন্ত্রণ করেন এই দুইজনই যেকোন মুহূর্তে ওবায়দুল কাদেরের মত নেতা তৈরি করার ক্ষমতা রাখে আবার ছুড়েও পেলে দিতে পারে। ভবিষ্যতের ইতিহাসে শাসক হিসেবে তাদের নাম থেকেই যাবে যতদিন বাংলাদেশে আছে।কিন্তু এই ওবায়দুল কাদের সাহেব কে দশ বছর আগেই অনেকেই চিনত না আর বিশ বছর পরে কেউ চিনবেও না কতটুকু কান্ড ঞ্জানহীন হলে বলা যায় খালেদা জিয়ার চেয়ে ওবায়দুল কাদের বড় এটা হাইস্যকর।,0,politics
কাউয়া বাদেয়া দরকার,0,politics
পুরনোগুলোর তো খাওয়া শেষ এখন নতুন গুলো এসে আবার লুটে পুটে খাবে আর কি,0,politics
আপনার কথা থেকেই বুঝা যাচ্ছে আপনি বি এম পি এর পা চাটেন। বর্তমানে কোনো দলের নেতাকর্মীই ভালো না।,0,politics
তানাহলে অবরারের মতো নিস পাপ নির অপরাধ একটি ছেলেকে বিশ্যোবিদ্যালয়ে রড দিয়েকুপিয়ে কুপিয়ে মধয়ো জুগি কায়দায় মারলো কুত্তা লিগ তারপর এইজে নুরুল হকনুর কে এবং তাসহছাএ দের এরকিকোনো বিচার হলো নাকোনো সনএাস ধরাপরলো তাহলে দেশের জন্যো মানুষ এগিয়ে আসবেকিভাবে সেটাআপনারাই বলেন,0,politics
বেটি যেই ভাবে খালেদা জিয়ার গুণগান গাইলো তাতে মনে হলো দেশটা খালেদা ছাড়া কিছুই না।,0,politics
খালেদা গনমানুষের নেতা,0,politics
টিচার এতটা মিথ্যা কথা বলে জানা ছিল না,0,politics
ভোট চুরি করলেন বেশি দিন হয় নি উকিল সাহেবা!,0,politics
ভাই আমরা তো ঠিকমতো ভোট দিতে পারি না ভোট দিতে গেলে পুলিশ আগে দেখে ধানের শীষে দিচ্ছি না নৌকা মার্কায় দিচ্ছে যদি দেখে ধানের শীষে দেই তাহলে জেলে রাষ্ট্রবিরোধী মামলা এক কথায় বলতে গেলে আমরা জেলের মধ্যে আছি আর বাংলাদেশ হলো সেই যে কিছু বললেই ছাত্রলীগ পিটাবে পুলিশে সেভাবে যুবলীগের থাকে তাদের কেউ নাই এর জন্যই মনে হয় বঙ্গবন্ধুকে হত্যা করে ছিল সালে এখন আমার মনে হয় শেখ হাসিনার এই হাল হবে,0,politics
জামায়াত শিবির নূরুল হকের মাধ্যমে হল দখলে নেমেছে।সরকারের উচিত নূরুল হকসহ ওদের দলের বিরুদ্ধে ব্যবস্থা নেয়া।,0,politics
কাদের একটা দালাল ওর দুর্নীতি সরকার দেকবানা,0,politics
এমন বাবে চিন্তা করার জন্য এবং আমাদের সামনে আনার জন্য অনেক ধন্যবাদ,0,politics
তুই ইনু আওয়ামীলীগে থাকলে ও বি এন পি জিতবে না থাকলে ও বি এন পি জিতবে।তার পর তুই ইনু বেয়াদবির সাজা পাবি ইনশা আল্লাহ।,0,politics
নুরু ভাই।। তোমাকে ভবিষ্যত এ বাংলার নেতা হিসাবে দেখতে চাই,0,politics
আওয়ামীলীগ গরিবের সরকার নয় বড় লোকদের সরকার,0,politics
দেশটা কিন্তু রাজতন্ত্র না। গনতন্ত্র দেশ বাংলাদেশ। জনগন সব চাইতে বেশি চায় কাকে এটা জনগনেই ভালো জানে।,0,politics
দিপু মনিরে দিবো,0,politics
এই দেশে আমরা বাস করি যেখানে বিচারের বি প্রযন্ত উচ্চারণ করা যায় না আমি আশা করি কুকুরের রাজত্ত আর বেশি দিন থাকবে না কারন। কুকুরের মরন আসলে মুরগির ছা খায়।।অদের অবস্তাও এখন সেম,0,politics
পাপের রাজ্জে ভাল মানুষের মুল্য নেই,0,politics
বেশি প্রতিবাদ করব না আওমীলীগ বলে কথা চাকরি থাকবে না,0,politics
এই শিক্ষক টা দালাল,0,politics
গুজবে কান দিবেন না! এগুলা ! 😆😆😂,0,politics
তোমার এতে টাটায় কেন,0,politics
ও স্যার কে জুতা পিঠালে ভালো হবে,0,politics
ইনু সাহেবের কথাগুলো একদম সত্য ।,0,politics
ছেড়েই যেতে হবে সব জিবনের কলরব,0,politics
দেখেন ভাই আবার এই ভিডিওর জন্য আপনার চ্যানেল বন্ধ না করে দেই।।। কখন কি হয় এ দেশে কেউ জানে না বুঝতেউ চাই না।,0,politics
ভাই আরো ভালো চাই,0,politics
এবার যে কোন দলে যাবে,0,politics
ওয়াও দারুণ খবর তো এই দারুণ খবরটি উপস্থাপন করার জন্য অসংখ্য ধন্যবাদ।,0,politics
এটাও হাছিনার চাল,0,politics
নুর ভাইয়ের কথা গুলো সম্পুর্ন সঠিক ছিল,0,politics
আওমালীগ একা একশ,0,politics
তোমার দাম তাহলে এক পয়সা,0,politics
কয়েকদিন আগে লন্ডন গিয়ে খাট কাপাইয়া এখন সংসদ কাপাচ্ছে,0,politics
কথা কেনো ওকে ধুনে ফেলো আর ছাএলীগ ভুলে যাসনে এক মাঘে শীত যায়না তোদের গোস্ত ও একদিন কুওাকে খাওয়ানো হবে অনেক বেড়ে গেছত তোরা,0,politics
এটা কোন কথা কোথায় রাজরানী কোথায় বিছনায় মুতুনি,0,politics
ধন্যবাদ স্যারকে তবে উনি নিজে এভাবে রাস্তায় নামার কারনে জ্যামটা আরও বেশি হয়েছে মেবি।,0,politics
এ বি এম পির বেয়াদ্দপ,0,politics
মাওলানা ভাসানীর মুক্তিযুদ্ধ পূর্ব আওয়ামী লীগ আর আজকের আওয়ামী লীগের মাঝে আকাশ পাতাল তফাৎ। জনগণের সাথে যে জুলুম করছে পৃথিবীতে ভোগ করে যাও পরকালে শাস্তি নিশ্চয়ই পাবে। সবাই সামনে সালাম দেয় কিন্তু মনে মনে ঠিকই থুথু দেয়।,0,politics
আরে গাধা বাপ্পী লাহিড়ী সোনা পছন্দ করেন এবং তার শরীরে কমপক্ষে কয়েক কেজি সোনা আছে ওবাদুল কাদের ঘড়ি পছন্দ করেন উনি না খেয়েও ঘড়ি কিনবে এটাই সত্য,0,politics
আমার অফিসের পিয়োন ও ম পাস। খালেদা জিয়া ও ম পাস। আমার অফিসের পিয়োন প্রধানমন্ত্রী হলে অবাগ হওয়ার কিছু থাকবেনা।,0,politics
তারা সব করতে পারবে কারন তাদের দেশ আর সারা দেশের মানুষ রহিংগা,0,politics
শিক্ষা প্রতিষ্ঠানে আগুন জ্বালাতে বলে স্লোগান দেয়। এরা বলে স্টুডেন্ট হাহাহা।,0,politics
এটা না এখন তারা তারাই নাটক করবে।,0,politics
ডানডি মানডি নিয়ে বসাটা ওচিত হয় নি। এ সব হাজারো কাদের আসলে ও নেএী খালেদা জিয়ার মত হবে না,0,politics
যারা কমেন্ট করছেন দয়া করে বানান ঠিক রাখুন। উত্তেজিত অবস্থায় দ্রুত কমেন্ট করতে গিয়ে বানান ভুল করবেন না। আমরা যারা কমেন্ট পড়তে আসি আমাদের পড়তে বেশ অসুবিধা হয়। জনস্বার্থেঃ কমেন্ট রিডার এসোসিয়েশন অব বাংলাদেশ।,0,politics
আগে নিজেদের কাগজ সঠিক করেন,0,politics
হাসিনা তাদেরকে দিয়ে অনেক অবৈধ কাজ করিয়ে এখন তাদেরকে ছুড়ে ফেলে দিচ্ছে। এখন কাউয়ার মতো তাদেরকে জনগণ ছিঁড়ে ছিঁড়ে খাবে।এটাই হাসিনার টেকনিক। 🤗,0,politics
সব কথার ভিতরে একটা কথা কিন্তু সত্য ছিল ইনু সাহেব সেটা হচ্ছে আপনারা সবাই মিলে বিএনপি র বিরোধী একটি ঐক্য ও তৈরি করেছেন।,0,politics
পরিবর্তন করলেই ভাল হবে।,0,politics
আপনাকে কোনো না কোনো ভাবে আইনের আওতায় আনা হবে।,0,politics
কেউ আমাকে বলবেন মালাউন শব্দের অর্থ কি?,0,politics
এগুলা নিয়া মিডিয়া আসবে না আসবে বিরোধীদলের ফোন আলাপ ফাঁশ,0,politics
চালি জান ভাই,0,politics
উপু উকিল তুই,0,politics
কাউয়া,0,politics
সঠিক বিচার চাই,0,politics
ভাই ভিডিও কেটে দেখান কেন,0,politics
আরে ওবায়দুল কাদের সেত কথা বলতে পারে না,0,politics
মজু না টজু হেতি কি পাগল নাকি ছাগল,0,politics
আমাদের মতো সাধারন মানুষের জন্য নতুন নতুন কিছু চাই।,0,politics
সত্যিকারঅর্থে যিনি সৎ তিনিই বড় কোন দূর্নিবাজ জেলের কয়াতি অবশ্যই বড় হতে পারেনা হে বয়স ও দূর্নিতির দিকটায় বিবেচনা করলে খালেদাকে নাম্বার বা বড় বলা যায়,0,politics
ঢাকা বিশ্ববিদ্যালয়ে আগে মানুষরা লেখাপড়া করতো। এখন জানোয়াররা পড়ে। আপনারা আরেকটি বঙ্গবন্ধু সৃষ্টি করছেন৷,0,politics
আওয়ামী ছাএলীগ এখন বেশ্যা আর খদ্দের চরিএ ধারন করেছে। দলবাজ শিক্ষক রা দেশ কে ডাস্টবিন বানাচ্ছে!,0,politics
কাদের সাহেবকে অসংখ্য ধন্যবাদ উনি ঘড়ি হাতেপরেন আমি ভাই ঘড়ি পরিনা এটা একটা বোঝা তবে আপনার জালায় মানুষ ঘড়িপরা বাদদিবে।,0,politics
ওবায়দুল কাদের জেটা পারে খালেদা জিয়া সেই টা পারেন নাই,0,politics
হা হা ছাগলের সাথে কার তুলনা।।।।,0,politics
দিন দিন শিক্ষা বাড়লে বিএনপি থাকবে নাহ কারন বিএনপি কোনো সুস্থ মানুষ সাপোট করতে পারে না,0,politics
বাংলাদেশের এমপি মন্ত্রী হয়েও যদি এই দামি ঘড়ি ব্যবহার করতে না পারে তাহলে এই ঘড়ি কারা পড়বে। নাকি বাঙালি হওয়ার কারণে এগুলো ব্যবহার করা যাবে না। টেকনিক বাজ দালাল।,0,politics
কাকের কাদেরের পরিবর্তন তো অবশ্যই দরকার। কিন্তু সাথে সাথে ময়ূর রুপি সভাপতিরও পরিবর্তন বাঞ্ছনীয়। কারণ এদের মধ্যে কুকর্মের কয়লা এতো বৃদ্ধি পেয়েছে যে কামার শালার লোহার সংস্পর্শে এদের আনা উচিত!!!,0,politics
সত্যিই আপনি অনেক সাহসী দোয়া করি সবসময় আমাদেরকে দেখিয়ে যাবেন।,0,politics
তুই বা তোরা পাপি কেল্প।,0,politics
সোহেল তাজকে সাধারণ সম্পাদক হিসেবে জাতি দেখতে ছাই,0,politics
ভিডিওটা খুব সুন্দর লাগছে এরকম ভিডিও আরো অনেক অনেক শেয়ার করো বন্ধুরা,0,politics
সালার পাপ জোয়ান হয়েছে মরেজা,0,politics
সময় বেশি দুরেনা।ইনুর অবস্থা ইমরান এইচের মত হতে যাচ্ছে।।।,0,politics
ছাএলীগ মানেই ময়লা আর্বজনা ওদের কে বয়কট করুন ওদের লজ্জা শরম বলতে কিছু নেই,0,politics
আওয়ামী লীগ জে কি দেশের মানুষ জানে,0,politics
নুর হচ্ছে আগামীর তরুণ সমাজের নেতা। যতই হেলমেট লীগ ডিম লীগ বের হোক না কেনো একদিন না একদিন তাদের বিচারের মুখোমুখি হতেই হবে ।,0,politics
পরিবার ভিত্তিক রাজনীতি। হাসিনা হলো মাদার তেরেসা। তাকে সবাই পুজা করে। সব যদি পরিবর্তন হয় সভাপতি কেন নয়? তিনি কি আমৃত্যু সভাপতি থাকবেন।,0,politics
কা কা কা,0,politics
বেগম খালেদাজিয়ার সাথে তুলনা শুধুই বেগম খালেদাজিয়ার,0,politics
বাংলা দেশের মানুষ এত কথা বলে। ওরে পাগল খালেদা জিয়া মানি সানতি ওবায়দুল মানি শয়তানের হাড্ডি।,0,politics
মার হাবা😂😂😂😂,0,politics
যে দেশে জুলুম থাকবে এবং প্রতিনিয়ত মজলুমের দীর্ঘ শ্বাসে আকাশ বাতাস ভারী হচ্ছে সেদেশ কখনো শান্তি আসবে না। এদেশ কে সুখ সমৃদ্ধি ও শান্তিময় করতে হলে মানুষের উপর জুলুম অত্যাচার দূর করতে হবে।,0,politics
দেখেন ভাই কিছু না কিছুর লোভ তো থাকতে হবে মানুষের তাই না! ক্যাশটাকা থাকলে প্রবলেম সোনাদানা থাকলে প্রবলেম জমি বাড়ি গাড়ি থাকলেও প্রবলেম এখন ঘড়ি থাকলেও আপনাদের প্রবলেম? কাউয়াটাকে কি একটু শান্তিতেও থাকতে দিবেন না আপনারা?,0,politics
চুরা জাফউল্লা,0,politics
কৈ রলো শাহাজাদী আর কৈরলো ছাগলেরলাদী,0,politics
নুর ভাই অদের বিচার হবে,0,politics
অপু একটা বিয়াদব সেটা সবাই যানে।,0,politics
করলাম,0,politics
ইনুর কাছে জেই তেল আছে আমার মনে হয় তেলের কমপানিতে এত তেল নাই শেখ হাছিনা তাকে আরু আগে বিদায় দেয়া উচিত ছিল ইনু এখন লেজ কাটা কুতি জেই পাইবে সেই করবে হা হা হা,0,politics
আপনারা পেন কেমারা ব্যবহার করুন,0,politics
দেশোদহী,0,politics
এরা বংগ বনদু টেবলেট খাইচে আর কিচুনা,0,politics
সাহেদ সাহেব বাই আসসালামু আলাইকুম এগুলো বললে কবেযে আপনাকে গ্রেপতার করে বলা যায় না হা হা,0,politics
ভাই দলমতের উর্ধে এসে একটি কথা বলি। কেউ কিছু মনে করবেন না। আমি রোমানিয়া থাকি। ছোট একটা চাকরি করি। আমার মত খুদ্র একটা মানুষ যদি ব্রান্ড এর সিরিজের মডেলের যার বাংলাদেশের টাকা অনুযায়ি টাকা দামের ঘড়ি হাতে দিতে পারি তাহলে ওবায়দুল সাহেবের মত একজন প্রবীন রাজনৈতিক ব্যাক্তি এবং সফল ব্যাবসায়ী কেন দামি দামি ঘড়ি হাতে দিতে পারবে না???,0,politics
যেকোন সময় ভিপি নুর এর প্রান নাষের চেষ্টা চালাতে পারে সন্ত্রাসীরা আল্লাহ সকল মায়ের সন্তানদের হেফাজত করুন আমিন।,0,politics
মিথ্যাচার চাটুকারিতা নিন্দা ছাড়া দেশ ও দশের উন্নয়নের কোন কথা তার মুখে শুনলাম না!!,0,politics
দেখে মনে হচ্ছে তামিল মুভি দেখছি। নাটক আর কত প্রকার হতে পারে।,0,politics
ঢাবির ইতিহাসকে তোরা কলংকিত আবারো।,0,politics
সেই কাগজ কোথায় বেটা চাপা মেরে খাস দশ হাজার টাকার ঘরি পরিস তুই তো দনের বাল,0,politics
হা হা হা এরাই হাসিনার সোনার ছেলেরা।,0,politics
মহিলা মাতাল,0,politics
চুরের মার বরোগলা,0,politics
হা হা হা নারী নেএীত্ত হারাম আজ বুজতে পেরেছে মানুষ জা সারে বছর আগে বলেছিল মোহাম্মদ সাঃ কে অপমান করে কখনো শাত্তি পাওয়া জাবে না,0,politics
টিক বলছে ভাই,0,politics
নিচ্ছয় এইখানে বিএনপির কোনো ✋আছে তানা হয় এতো দামের ঘরি কি ভাবে পরে বাবার বিষয়।,0,politics
মন্ত্রি সাহেবের তো ভালই ক্ষমতা দেখতাছি এতো লোকজন নিয়া ঘুরতেছে 😂😂,0,politics
ভাই আপ‌নি তো ম‌ন্ত্রি সা‌হেব কে হি‌রো থে‌কে সুপার হি‌রো বানাইয়া দি‌লেন!,0,politics
উনি থেকে মাস্টার কপি কিনছেন আপনার অসুবিধা আছে?,0,politics
খালেদা জিয়ার সাথে কাদের এর তুলনা মজা পাইলাম,0,politics
কাউয়া কে লাথি মেরে ফেলে দেওয়া দরকার,0,politics
ধন্যবাদ ভাই,0,politics
ভালোবাসা অবিরাম,0,politics
আপনার কাছে আমার ছোট একটা প্রশ্ন। দয়া করে বলবেন। বাংলাদেশে রাজাকার কারা ও যংগী কারা আর তেঁতুল হুজুর কারা। আপনি আল কোরআন এর অর্থ একটু শুনেন বা একটু পরেন। সকল রাজনৈতিক দলের নেতা কর্মীদের বলছি। এতে আপনার নিজেরই লাব হবে।,0,politics
এরাও মানুষ?,0,politics
ভাই সব হাসিনার নাটক,0,politics
সিট বেল্ট না লাগানো কি অপরাধ নয়??? মন্ত্রী মহোদয় এবং উনার গাড়ী চালক দুজনের কেউই সিট বেল্ট লাগাননি!!!,0,politics
সবার বড় কে?? নোয়াখালীর রাষ্ট্রের প্রেসিডেন্ট কাউয়া কাদের🐦😂,0,politics
★★প্রধান মন্ত্রীর ভাষনঃঃ পিয়াজের দাম বেশি যবাই করলে খাশি নেই কোন সমস্যা আমি তোমাদের ভরসা কারণঃপিয়াজ ছাড়াও রান্না করা যায় ভোট ছাড়াও এমপি হওয়া যায় জনগনের সমর্থন ছাড়াও প্রধান মন্ত্রী হওয়া যায় স্বাধীনতার পক্ষের মানুষকেও রাজাকার বানানো যায় প্রকৃত রাজাকার হলেও মন্ত্রী হওয়া যায় লেখা পড়া ছাড়াও পাস করা যায় এটাই ডিজি টাল বাংলসদেশ।,0,politics
আল্লাহ আমাদের সবাইকে বাচাও,0,politics
আওয়ামী লীগ নেতা রা বেশিরভাগ দুর্নীতিগ্রস্ত,0,politics
প্রিয় ভাইয়ারা জলদি চিন্হিত করো এই অবৈধ সন্ত্রাষ ও দল কারা?? তাদের জলদি আলাদা করে দাও। লড়তে তো আমাদের ও তোমাদের ই হবে।,0,politics
আরে বিএনপিরা অরে এতো দামি ঘরি গিফট করে ফাসাই দিছে। 🤣,0,politics
বাহ বামাতি রাও দেখি এখন জামাতী দের সাথে!,0,politics
হায়রে শিক্ষক আর কত দালালী করবি মিথ্যা বলে ছাত্রদের কাছে কি ভাবে ধরা খেল তার পরও লজ্জা করে না ছি শিক্ষক ছি,0,politics
কি হইছে ও খানে কিছু বুঝলাম না একটু খুলে বলেন,0,politics
মরলে উর জানাজা নাই,0,politics
ইনুর দিন শেষ,0,politics
বেয়াদবরা,0,politics
কি যে লিখবো হাস্যকর বিষয়টি বিড়াল নিজের দিকে চেয়ে বলে আমিই বাগ,0,politics
কাউয়ার ভন্ডামি।,0,politics
এবার বুজেন জিকে শামিম বা সম্রাটরা কোমরের জোর কোথায় পায়।,0,politics
আগে জানতাম ওনি নারীদের কাছে অনেক প্রিয় একজন নেতা। এখন জানতে পারলাম ওনি ঘড়িদের কাছেও জনপ্রিয় নেতা। ঘড়ি বনাম তরুণী ওবায়দুল কাদের।,0,politics
রাইট রাইট রাইট,0,politics
বেগম খালেদা জিয়ার সাথে শেখ হাসিনার তুলানা হবেনা আর কোথায় কাদের,0,politics
কোথায় বাঘ আর কোথায় কুকুর,0,politics
ঐক্যের কথা বলে মন্ত্রী পাওয়ার ধান্দা! 😁,0,politics
চুরির টাকা খেতে থাকো বাবু সময় আর বেশি না তোমাদের,0,politics
সালার আওয়ামী লীগ পাগলের সাথে কথা না বলাই ভালো কোথায় ইজ্জত আলী আর কোথায় জুতার কালি,0,politics
কিসের ভুল বুঝাবুঝি কিসের সত্য গোপন করচ কেন,0,politics
কা কা কা কা বলুন তো এই কাউয়া টা কে??,0,politics
ভাই আরো ভিডিও চাই😍,0,politics
হেতি দেশিদ্রোহিরে। দেশবিদ্রহী বলে হেতি নাকি আবার নেত্রি। বিচার হবে কেয়ামতের দিন এই যে এত মিথ্যা কথা বলেন সব বিচার নিশ্চিত থাকুন,0,politics
ওরে ওবায়দুল কাদের তুই যতো খুশি ততো ইনজয় কর আর অপেক্ষা কর আল্লাহর হুকুম আসার আগ পর্যন্ত,0,politics
আমার সোনার খবর,0,politics
এমপি মোস্তাফিজুর রহমান আমাদের এমপি 😂😎,0,politics
হ্যাঁ সেরা সত্য কথাগুলো তুলে ধরার জন্য তোমাকে অনেক ভালোবাসি ভাই😍😍,0,politics
সবাই এক সাথে মিলাও ছাত্রলীগ বস্তা ভর।,0,politics
🤧🤧🤧🤧🤧🤧ওবাদুল্লাহ,0,politics
এরা ভার্সিটিতে পড়ালেখা করে দেশের জন্য কিছু উপহার দিবে? নাকি ভার্সিটিতে রাজনীতি করে পরবর্তী মন্ত্রী মিনিস্টার হওয়ার স্বপ্ন দেখছে!! হায়রে পাগল আমও যাবে ছালাও যাবে,0,politics
ব্যা ধারোন,0,politics
নুরৃকে।কেন।মারে।বার।বার।হাছিনা।মাগির।দোষ।সব।আমিবলসি।পুলিশ।লিগ।চাএ।লিগ।সব।হাছিনার।লোক।ভারত।মদি।র।লোক।,0,politics
সুস্ট নির্বাচনের মাধ্যমে ক্ষমতা বদলের ব্যবস্থা ধ্বংস করা হয়েছে বলে অপু গন্গ্ এরা ঢালাও ভাবে মিথ্যা বলতে পারছে। নাহলে মুখ দিয়ে কথাতো দুর পাছা দিয়ে পাতলা পয়খানার সাথে নাড়িভুঁড়িও বের হয়ে যেত।,0,politics
ভালো কোন আলেম কে একটা পদ দিলে ভালো হত আল্লাহর ভয় থাকতো,0,politics
শেষ মেশ টিস্যু পেপার হইলি ইনু,0,politics
অপু উকিল মত এসব ফালতু লোক দের কেন যে টকশো তে আনে বুঝি নাহ এই অপু উকিল নিজ দলে তো দাম পাই নাহ তাই তারজন্য টকশো তে হাসান মাহমুদ আর ইনু মত বিএনপি কে যত গালাগালি করতে পারে কারন তিনি মনে করেন বিএনপি কে গালি দিলে তিনি নিজ দলে দাম পাবেন,0,politics
নিয়মিত অাসবেন,0,politics
এই প্রশ্নটা এখানে তোলাই হলো বেয়াদবি কারণ কোথায় খালেদা জিয়া এবং কি এমন ওবায়দুল কাদের,0,politics
কাকা কাকা,0,politics
ছোটলোক সাংবাদিক যদিও আপনি তাও এসব বিষয় নিয়ে ভিডিও বানানোর জন্য ধন্যবাদ,0,politics
কা কা কা উয়া,0,politics
আরে ভাই উনি ক্ষমতাশীন দলের সাধারন সম্পাদক সাথে উনি সরকারের বড় একটি মন্ত্রনালয়ের মন্ত্রী তাকে তো অনেক ব্যবসায়ী বা কূটনৈতিকরাও তো গিফট করতে পারে সাধারনত ব্যবসায়ীরা বা কূটনৈতিকরা সব সময় চায় সরকারের বড় বড় নেতাদেরকে হাতে রাখতে এতে তাদের ব্যবসা বানিজ্যের প্রসার হয় এখন তারা হাত করে ঐ সব নেতাদের কোন জিনিসের প্রতি দূর্বলতা আছে সেটার উপর ওবায়দুল কাদেরর হয়তো ঘড়ির প্রতি দূর্বলতা আছে তাই তাকে ঘড়ি দিয়ে হাত করছে আবার কেউ বা নারী বি পজিটিভ 😃😃😃😁,0,politics
শাবাশ শাবাশ শাবাশ একাই তিনশো।ভক্তিতা নয় যেন বাঘিনীর গর্জন। অসংখ্য ধন্যবাদ ব্যারিষ্টার রোমিন আফা।,0,politics
এরকম চোর বাটপার আরো দরকার বাংলাদেশ,0,politics
বেপক বিনোদন,0,politics
কাউয়ার কি হবে,0,politics
সরকারের বিরুদ্ধে যাতে ছাত্র সমাজ কথা বলতে না পারে সেইজন্য নরুকে ভিপি নিরবাচিত করে সব সময় বিভিন্ন রকম সমস্যার সৃষ্টি করে রেখে দৃষ্টি অন্যদিকে ব্যাস্ত রাখেবে সরকার। যাতে করে সরকারের অপকর্রমের কথা কেও চিন্তাও করতে না পারে। তাই গুন্ডালীগ এই ধরনের কাজ করমের মাধ্যমে ছাত্রদেরকে ব্যস্ত রাখবে। তাদের উদ্দেশ্যে সফল হচ্ছে েএবং হতে থাকবে। তাদের বুদ্ধি ও কুটরাজনিতী বুঝার ক্ষমতা সাধারণ ছাত্র বা নুরুদের নেই। বুঝার ক্ষমতা থাকলে নরু কখনই ভিপি হিসাবে শফথ নিত না।,0,politics
আমি আওয়ামিলীগ সরকার এর নতুন গণতন্ত্রের সংজ্ঞাটা জানতে চাই কেউ জানলে বলবেন ?,0,politics
সরকারি চাকরিজীবীরা চোর হতে পারলে তার মানে আমাদের মত সাধারণ মানুষেরাই সরকারি চাকরিজীবী তাহলে মন্ত্রী তো অবশ্যই হবে আর একটা কথা এখান তে বছর আগে দুই নাম্বারি হয় না এরকম কোন কথা নেই কারণ সে সময় মানুষ এত ইন্টারনেট ব্যবহার করত না আর আমাদের মত সাধারণ মানুষের কাছে ইন্টারনেট নেই বললেই হয় পথছিল একমাত্র নিউজ পেপার আর টিভি দেখা ছাড়া নিউজ পেত না তারপরেও সঠিক নিউজ আসতো এরকম কোন কথা ঠিক ছিল না তাই আমরা সব সময় অজানাই ছিল বললে চলে,0,politics
এ বি ডি তোমার কে কইসে কাউয়া কাদের সড়ক পরিবহন ও সেতুমন্ত্রী সে কাউয়া কুত্তা গরু ছাগলের মন্ত্রী,0,politics
ভাই এটা নরেন্দ্র মোদির দেয়া উপহার,0,politics
ইনু তুই বিনপি তে যোগ দে নইলে আমলীগ তোকে খেয়ে ফেলবে,0,politics
আপনার মতো দনের বাল যদি দশ হাজার টাকার ঘরি পরে তাহলে কাদের পরতে পারে দশ কোটি টাকার,0,politics
আওয়ামীলীগ এক অসভ্য! জাতি।,0,politics
কাউয়া বাংলা কথা বলতে পারে কেনো,0,politics
হাহাহা কুকুরের সাথে সিংহর তুলনা করে এই মহিলাকে কেউ দয়া করে পাবনা হাসপাতালে পাঠাও কেউ দয়া করো,0,politics
সাহসী ইউটিউবার ✌✌,0,politics
সুপার বস,0,politics
বি আর টি এর দুনীতি সামলান এক বছরেও লাইসেন্স পাচ্ছি না,0,politics
অপুর কথা শুনে হাসি আসছে,0,politics
সেলুট বেগম খালেদা জিয়া হাজারো সালাম আপনাকে,0,politics
আমি মুক্তিযুদ্ধের বীরদের দেখিনি কিন্তু আমি নুরুকে দেখেছি।,0,politics
জামাত এবং বিএনপি একই মায়ের পেটের দুটি সহোদর ভাই। ব্যারিস্টার রুমিন ফারহানা। আপাজী আপনারা এবং আপনাদের নেত্রী খালেদা জিয়া যে কত বড় অতুলনীয় জিনিস সেটা আমরা চোখ বন্ধ করেই বুঝতে পারি।,0,politics
একটা ডিম নিয়া এত কামরা কামরি হসি পাচ্ছে! হলের ভিতর পারমিশন ছারা গিয়ে নিজেই আইন লঙ্গন ওরা আবার আইন শিখাতে এসেছে?,0,politics
এক টা ঘড়ির দাম দিয়েই জিবন চেঞ্জ হয়ে যায় আমার মত মানুষের রাজনীতি।।,0,politics
ওবায়ুদুলকে দল থেকে বাদ দেওয়া উচিত বিচারের কাট ঘরায় নেওয়া উচিত।,0,politics
ভাই কেওকমেনকরে বিপদে পরোনা। কেনোনা একজন ভেজালে আসে,0,politics
উনিতো সব সময় শেখ হাসিনার সাথে সাথে থাকে তো সেখ হাসিনার চোখে পরে না ? চোরের দল সব সাধারন জনগনের টাকায় ফুটানি করে,0,politics
চাদের সাথে মাটির তুলনা হয় না,0,politics
কাউয়ার সঙ্গে খালেদা জিয়ার তুলনা হাস্যকর?,0,politics
বাংলাদেশের আওয়ামী লীগের সাংবাদিক দেখে না চক অন্ধ।,0,politics
ভোট পাইয়া ত পাস করে নাই তাই এমন,0,politics
দুয়া করি আল্লাহ কাছে আপনার জন্য,0,politics
ভাই সরকার আর সরকারের সকল নেতারাই অন্যায় এবং অন্যায়কারীর বিরুদ্ধেই কথা বলে।হোক সে ওবায়দুল কাদের আর অন্য কোনো নেতা।অন্তত আমি তো সারা জীবন এটাই দেখে আসলাম।যদিও আমার বয়স মাত্রবছর । তো সন্ত্রাসবাদ ছরাই কারা এদেরকে টাকা পয়সা দিয়ে পোষে কারা? এই সকল নেতারাই এদেরকে টাকা পয়সা দিয়ে পোষে। শুনতে খারাপ লাগলেও এটাই করুন বাস্তবতা। ভাইরে যদি মাথার উপর ছাদ না থাকে তবে কেও ঘরে দামি জিনিস পত্র রাখার চিন্তা করে না। তাই মাথার ওপর নেতার হাত না থাকলে দলের জন্য কাউকে খুন করার মতো সাহস কারর হবেনা। ক্যামেরার সামনে এসে যতই বগর বগর করুক জনগন কিছু আজো বোঝে। সকলেই তো আর সরকারের পা চাটে না।,0,politics
কনে জুতার কালি কনে লিয়াকত আলী মজা পাইলাম নানী🤣🤣 কাউয়া ঠাপি👺👺,0,politics
ভিডিওটি যদি সত্য হয় তা হলে সরকারের তদন্ত করা উচিত ।,0,politics
মাননীয় প্রধানমন্ত্রী আপনার এই সন্ত্রাসী বাহিনী থামান না কিন্তু ছাত্রসমাজ একবার জ্বেগে উঠলে আপনার চেয়ারটা হারিয়ে ফেলবেন।,0,politics
পিটানো দরকার! বিটিভির সংবাদ,0,politics
ভাই এগুলো গিফট্‌ পাওয়া গড়ি সে ব্যবহার করতেছেন আর এটা নিয়ে বেশি সমালোচনার দরকার ছিল বলে মনে করিনা আর আপনি বেশি যা দেখাইতেছেন সব এডিট করা আপনাকে কেউ গিফট্‌ করলে আপনিও ব্যবহার করতেন ঘরে ফেলে রাখতেন না আর আপনাকে একটা কথা বলি এইভাবে অপপ্রচার করা বন্ধ করেন।,0,politics
দেশের জনগনের টাকা দিয়ে ফুতী করা অনেক মজা হায় হায় লজ্জা কি দিয়ে ডাকব?,0,politics
ডিম লীগ।,0,politics
আপু আমি আশুগঞ্জ এর আপনার জন্ম ইসতান কোথায় দোয়া করি দয়াল তোমার শরীর ভালো রাখে রুমি আপু।ঐ আপু টাকে বলি চিল্লাইয়া ফাল্লাইয়া মার্কেট পাওয়া যাবে। পাবলিক এখন মারাত্মক।,0,politics
অপু টকশোতে এসে মানসিকভাবে অসুস্থ হয়ে পড়েছেন বলে মনে হয়।,0,politics
উনার আত্মীয় স্বজন বন্ধু বান্ধব এগুলো উপহার হিসেবে দিয়েছে দুদকের রিপোর্ট,0,politics
অনেক দিন পর অনুসন্ধানী সাংবাদিকতার উপস্থাপন দেখলাম। ধন্যবাদ।,0,politics
আর কি সুনবো জারোজলীগে জেই কয়টা আছে হাতে গোনা কয়েকজন চারা সব চোরের গুসটি,0,politics
সালায় শিক্ষক নামে কলংকয় হায়রে স্যার দালালী না করে এর চাইতে কলায় রশি দিয়ে মরে জান।,0,politics
খালেদা জিয়া দেশে মানুষে চোখে মনি,0,politics
জনগণের টাকা,0,politics
আওয়ামী লীগ এখন জাতির বোঝা এই বোঝাকে ময়লার স্তুপে ফেলে দিতে হবে।,0,politics
ভালো লাগলো ভাই।,0,politics
খাওয়া কাদের,0,politics
কার সাথে কার সাথে তুলনা কোথায় বেগম খালেদাজিয়া আর কোথায় ওবাইদুর কাদের ! বেগম খালেদাজিয়াকে জামিন দেওয়ার জন্য অনুরোধ রইলো !,0,politics
তোদের এইটা রাজনৈতি না নোংরামি তোদের রাজনৈতিতে দেশের মানসম্মান সব শেষ।জানতাম ছাত্ররা দেশের উজ্জ্বল ভবিষ্যৎ। এখন দেখতেছি পুরোটাই উল্টো,0,politics
সেতো কিনে নাই গিফট পাইছে।,0,politics
একটারও জন্মের ঠিক নাই,0,politics
খালেদা আর হাছিনার সাথে মিল নেই আর কাদের কি পাগল ছাগল লীগ খালেদা জণগনের মা,0,politics
হাসান তেই শেষ তোর দাম কমেছে তুই বিতারিত।,0,politics
দারুণ ভাইয়া শো চালিয়ে যান 😃👍👍। সাদী।,0,politics
ওরে কেউ দে ।,0,politics
সুদে দিলা ভাই??,0,politics
এক কোটি টাকার ঘড়ির কেন ওবায়দুল কাদেরের হাতে ? এটা জনগনের সম্পদ।,0,politics
আপু আপনাকে অনেক অনেক ধন্যবাদ,0,politics
আমাদের এয়ারপোর্টের একটু যাওয়ার ব্যবস্থা টা ভালো করে,0,politics
শেষ টুকু পুরাই ফানি ছিল,0,politics
হালা নুরুরে হলে ঢুকাইয়া ডিম থেরাপি দেয়া হোজ,0,politics
কালা কাউয়া জোশ,0,politics
লীগের নাটক আর কত দেখব?? আল্লাহ এই সব নাটক থেকে তুমি আমাদের পরিত্রাণ দাও। আমিন।,0,politics
সাভাস বাঙ্গালী ভি পি নুরুল হক,0,politics
এখন কি হচ্ছে সুনি,0,politics
রুমিন অনেক কস্ট পেলাম আপনার মত সম্পন্ন একজন মানুষ অপুর মত এক জনের সাথে বাহাস !! মেনে নিতে পারলাম না ।,0,politics
আগে ভোট চুরির না করে অধিকার ফিরিয়ে দে,0,politics
আল্লাহ নূর ভাইকে হেফাজত করো,0,politics
আল্লাহ তোমার কাছে দোয়া করি তুমি বেগম খালেদা জিয়া কে সুষতু করে মুক্তি দাও,0,politics
এতই কি দেখালো এরা? দেখতে থাকো অভাগা বাঙালি আর ভুগতে থাকো। তাছাড়া কিছুই করার নাই তোমাদের। মেরুদণ্ডহীন জাতির আরও যে কত দূর্ভোগ কপালে আছে আল্লাহ পাকই ভালো জানেন।,0,politics
কিছু দিন ধরে শাহেদ আলম রূপ পালটিয়েছে বুঝতে পারছি না আসলে তিনি কোন নৌকার মাঝি,0,politics
অপু বিশ্বাস বাংলাদেশের প্রতিটি হিন্দুর মনে আগাত করেছে।এই মেয়ে কখনো সুখি হতে পারবেনা ।ভগবান এর বিচার করবেন।,0,politics
চোরের দল ✍আরমান জিহাদ তাঁরা নাকি দেশ গড়িবে সোনার বাংলা স্লোগানে লক্ষ কোটি মিথ্যা কথা শুনি তাদের জবানে। হয়তো আজকে মুক্তি পাচ্ছো সরকারী লোক বলিয়া দূর্নীতি আজ যেথা সেথা ব্যাংক ভরিতে মরিয়া। আর কতকাল খাইবি তোরা এই দেশটাকে লুটিয়া? দেশের মানুষ বিচার করতে উঠবে একদিন জাগিয়া। বালিশ ধান্দা পর্দা ধান্দা এবার আসলো টিউবলাইটে পুকুর খনন ভিজিট করতে একদল যাবে বিদেশে । দেশটা তোরা ভাবিস কেন লুটে খাওয়া জন্য উন্নয়নের নামে বল আর কিনবি কত পন্য?,0,politics
অপূূ কোথায় আর রূূমিন৷ কোথায়?,0,politics
চোররা তো পরবেই। দেশের টাকা চুরি করে এগুলা কিনে।,0,politics
এটার নাম আওয়ামী লীগ,0,politics
মিথ্যা আর কত বলবি।আওয়ামীলীগ,0,politics
কাক কাদের ইয়াবা বদির স্ত্রীকে এর নির্বাচনে নমিনেশন দিয়েছে কোটি টাকার বিনিময় এমন কথা বাজারে চালু আছে! শুধু ভোটচুরি নয় পুরো দেশটাকে এই পিশাচরা লুট করছে!,0,politics
লোক দেখানো কাজ আর কতদিন করবেন মন্ত্রিমশায় এই কাজ না হয় ট্রাফিক পুলিশ করুক আপনি খালি আপনার লোক জনদের আর নিজের চুরি আর দুর্নিতী বন্ধ করেন। পুরা রাস্তায় ট্রাফিক জ্যাম লাগায় লোকদেখানো কাজ করলেন আর এরপর আপনি রাস্তায় দাড়ায় বিরোধী দলকে দোষারোপ করে ভাষন দিবেন। এটাই আপনার উদ্দেশ্য,0,politics
নাটকটা ভাল,0,politics
কথায় লজিক ছিল ধন্যবাদ সাহেদ ভাই,0,politics
খুব সুন্দর একটি ভিডিও কিনতু অপু কোথায় ভাইয়া??,0,politics
ফারহানা রুমিন কিং,0,politics
অবশ্যই আপনার জন্য দোয়া থাকবে সবসময়।আর এই ভাবে সত্য ঘটনাগুলো উদ্ঘাটন করবেন,0,politics
আগুন জ্বালিয়ে দিব,0,politics
বাংলাদেশের আরেক নাম ছিলো পূর্ব পাকিস্তান এখন হয়েছে খালেদা জিয়া। আর খালেদা যে পাকিস্তানের এজেন্ট তারই বহিঃপ্রকাশ করলো চাপাবাজ ফালহাম গুমি ফারহান রুমি সরকার গণতন্ত্র পরিস্থিতি রাখায় এখনো টকশো তে চাপাবাজি করে চলতে পারছিস। না হয় পুটকির ছামড়া কোথায় যেতো।,0,politics
নিজের কামানো টাকা হতো তাহলে তো একটা পরা সম্ভব হতো কিনা তা ও সন্দেহ আছিল জনগণের টাকা চুরি করে লুটপাট করে ঘড়ি না আরো কত কিছুই করা সম্ভব এটা মাত্র ওবায়দুল কাদের না এটা লীগ নামক সংগঠনের যতগুলা নেতা নেত্রী আছে সবগুলা একি কয়ালেটি।,0,politics
কোথায় শেক সাদী আর কোথায় ছাগলের লাদি,0,politics
★সব সত্য একদিন ফাঁস হবে এবং মিথ্যাবাদী ও তাদের পরিবারের ধ্বংস হবে !,0,politics
নুরুল হক নুরু প্রতি আমার আহবান ছাএলীগ নয় সরকার পতন এর ডাক দিন আরো একটি এর যুদ্ধ দেখতে চাই সরকার পতন না হলে ছাএলীগ কে থামানো যাবে না ছাএদের সাথে বাংলার সাধারণ মানুষ সবাই আছে তুমরা সরকার পতন এর ডাক দিন,0,politics
হাজার টাকার অভাবে আজ মাস হল আমার মাসুম বাচ্চাদের কাছে যেতে পারছিনা 😢 জব বাদ দিয়ে কৃষি করি কোন ফসলের দাম নেই ! আর মুন্ত্রীর কটি টাকার ঘড়ি বিলাস হায় আল্লা তোমার কি চোখ কান বধির হয়ে গেছে 😓,0,politics
মার সালারে,0,politics
আগে মনে করতাম ঢাকা বিশ্ববিদ্যালয় স্যার রা অনেক জ্ঞানী এখন দেকছি এরা জ্ঞান পাপি । তোমরা জাতির লজ্জা।,0,politics
রাইট বার অপু কতা কম বলেন আমাদের পয়সাই দেশ চলে একানে মিত্যা বলে খোন লাব হবেনা,0,politics
উপহার হিসাবে পেতে পারেন।,0,politics
কাওয়ার সাথে খালেদা হাইস্যকর।বড়ই হাইস্যকর।ড়িমলীগেরর মগজগোলা পোকায় খেয়ে ফেলছে।চুরের মুখে চুরের চুরের কাহিনী।অপু উকিলের মুখে ডিম মারি।হেতিরে কাবিলার সাথে মিট করায় দে।কাবিলা ও মিথ্যা কথা কয়না।,0,politics
ছাত্রলীগ বাতিল করা হক🚫🚫🚫🚫🚫🚫🚫🚫🚫🚫🚫🚫🚫🚫🚫🚫🚫🚫🚫🚫🚫🚫🚫🚫🔞🔞🔞🔞🔞🔞🔞,0,politics
সুন্দর আলোচনা ।,0,politics
সালা তোর বাপের বয়েসি লকের সাথে কি ভাবে কথা বলতে হয় তাও জানস না,0,politics
মার সাথে ছেলে তুলনা হয় না,0,politics
এই টকশোটি করে খালেদা জিয়াকে কাদেরের মত একজন চরিত্রহীন নেতার সাথে তুলনা করাতে খালেদা জিয়াকে অপমান করা হয়েছে একইভাবে ঐ বখাটে মার্কা অপু উকিলকে এনে রুমিন ফারহানাকেও খাটো করা হয়েছে। টকশোবাজরা সাধুদের সাথে অসৎদের এ ধারার বস্তিমার্কা মিথ্যাচারের অত্যাচার আয়োজন করার প্রচেষ্টা বাদ দিন। আপনারা নিজেরাও জানেন এ সরকার আর তার দলের লাকগুলো কতটা অসৎ ও অমানুষ। আপনারা এসব করে ওদেরে মানুষ বানাতে পারবেন না। এসব দেখে সারা জাতি হাসবে না কাঁদবে? এদের অত্যাচারে একদিক মানুষ দীর্ঘশ াস ছাড়ছে অন্যদিকে ওদের ঐ মিথ্যাচারী বখওয়াজও তাদের শুনতে হচ্ছে এসব হচ্ছে মরা পথহারা সরকারের পক্ষে দালালী মঞ্চনাটক।,0,politics
কমেন্ট পড়ে যা বুঝলাম মহান মুক্তিযুদ্ধকে যারা বিকিকিনি করে তাদের গ্রহনযোগ্যতা জনগণের কাছে শুন্য,0,politics
আল্লা নুর ভাই হেপাজত করক আমিন,0,politics
ইনু সাহেব এবার কি হবে??,0,politics
ভাইরে ভয়ে আছি কোন দিন না জানি আপনাকেও গ্রেফতার করে নিয়ে যায়??,0,politics
কাদের কে বাদ দিলে বিনোদন দিবে কে দেশবাসীকে?,0,politics
বিয়াদবের বাচ্চা।,0,politics
অপু উকিল তোর মুখ দিয়ে কি কোনদিনও সত্য কথা বের হবে না? তোর মুখ এবং ব্যাক সাইট উভয়ই সমান রে। তোর জন্মই হয়েছিল মিথ্যা কথা আওড়ানোর জন্য।,0,politics
মুসা বিন শমসের,0,politics
এত সুন্দর করে মিথ্যা বলছে যে কথা বেধে বেধে যাচ্ছে এটা কে বলে আমীলীগ,0,politics
মজিবরের সাথে কউতুকে ভাল মানাবে,0,politics
ভিডিও করার জন্য আর কোনো লজিক পাস না। ফালতু কোথাকার।জুতা মারা করা উচিত তোকে,0,politics
অবৈধ ফাটাকেষ্ট।,0,politics
উনার শশুর আব্বা মনে হয় দিচ্ছেন,0,politics
এখন কি রাস্তা জ্যাম হয়না,0,politics
এয়াবা সম্রাট বদির ব্যপারে কি সিদ্ধান্ত নিচ্ছে সরকার জনগন তা দেখতে চাই আর ওবায়দুল কাদের কে বাদ দিলে অনেক ভাল হবে,0,politics
মাননীয় প্রধানমন্ত্রী দেশ রত্ন শেখ হাসিনা কে ধন্যবাদ জানাই এবং কি যেই সব এমপি মন্ত্রীর কারনে দলের মান সন্মান খুন্ন হবে তাদেরকে পদ থেকে বাদ দেওয়া দরকার আর সেতু মন্ত্রী ওবায়দুল কাদেরকে অবসর নেওয়া দরকার উনার দ্বারা অনেক ছেলেরা ছাত্র লীগের নাম দিয়ে খুন খারাবি চাঁদা বাজি দখল বাজি এই সব করে যাচ্ছে,0,politics
যারা দামি ঘড়ি পড়ে না তাদের মুক্তিযুদ্ধের চেতনা নাই।।।।😆😆😆😆,0,politics
যে দেশে নিরপরাধ মানুষ লাঞ্চিত হবে সেই দেশে ত আল্লাহর গজব আসবেই,0,politics
সাধারণ সম্পাদক হোক সোহেল তাজ,0,politics
আওয়ামিলীগের কাজই হলো সম্মানিত মানুষের বিরুদ্ধে অশালীন কতাবার্তা বলা,0,politics
আওয়ামিলীগ মানেই শতাব্দীর সেরা মুনাফেকের দল! এদের মুখের কথা আর মনের কথা কখনোই মিল থাকেনা! এক জনের ও না,0,politics
মেয়ে দের কে বলতে দিন,0,politics
একটা কাজের বুয়া দেশের প্রধানমন্ত্রী হয় কিভাবে,0,politics
এটা নাকি সাধীন দেশ,0,politics
কাদের সাহেবের সময় বাংলাদেশে মেগা প্রজেক্টে কাজ করা হচ্ছে সেই প্রজক্ট থেকে কতো শতকোটি লুটের টাকা পকেটে পুরছে!,0,politics
কি আর বলবো ভাই সবকিছুই উপর মহলের কারসাজি,0,politics
আওয়ামী লীগের এমপি মন্ত্রীরা জামায়াত বিএনপিকে ধ্বংস করার চেষ্টা তারা নিজেরাই ব্যর্থ হয়েছে মিথ্যা কথা বলতে বলতে তাদের মুখের মাধুর্য নষ্ট হয়ে গেছে মুনাফিক এ পরিণত হয়ে গেছে তারা,0,politics
কথা গুলো সঠিক।,0,politics
এটা আছে যুদি ভালো লাগে করেন প্লিজ,0,politics
আপনাদের মতো মানুষ এবং এমন নিরিক্ষা বিহীন মতামত দেশের সবচাইতে বড় শত্রু।।। দেশের উন্নয়নে সাহায্য করতে না পারলে ত্রুটিপূর্ন এবং মনগরা চিন্তা ধারা প্রচার করে বহিবিশ্বে দেশের ভাবমূর্তি নষ্ট করবেন না।।।সরকারের সমালোচনা না করে তাদের কাজে সাহায্যে করুন।।।এইভাবে জনপ্রিয়তা অর্জন করা যায় না।।।সরকারের সাথে না হোক নিজের মতো উন্নয়নে অংশ নিন।।। এর পর তা প্রচার করুন।।। জনগণের উন্নতি হবে।।।ধন্যবাদ।।।,0,politics
এটা দেখাও লজ্জা সুনায় লজ্জা ।,0,politics
রান্নার প্রতিটা হোটেল পানির প্রতিটা ট্যাংক গুদাম ঔষধের প্রতিটা কম্পানি খাবারের প্রতিটা ফ্যাক্টরি চেক করো আর ওদের এই ষড়যন্ত্রের অস্র কোথায় জমিয়েছে তা আগে খুজে বের করে ফেল।,0,politics
সেদিন বেশি দূরে নয় যেদিন পেন খুলতে হবে।,0,politics
আরে ভাই আপনার মাথায় কিছু আছে। কার সাথে কার তুলনা করেন। তিন তিন বারের প্রদান মন্ত্রী।,0,politics
এই বুড়ি মহিলাটি কে?,0,politics
ভাইজান আমি বলতে চাই আমার দেশের মানুষ না খেয়ে থাকে না।,0,politics
আল্লাহ হেফাজতে রাখো নূর ভাইকে,0,politics
জঙ্গি দর জঙ্গি মারো জঙ্গি বরো জেলে নিজের গরে খুইজা দেখো জঙ্গি তোমার চেলে,0,politics
যে দেশে সাধারণ ছাএ ছাএীর ভোটে বিজয়ী একজন ভিপি ভার্সিটিতে ছাএলীগ এর আক্রমনের শিকার হয় সেই দেশে আবার কিসের স্বাদিনতা আমার দেশ দুনিয়ার ইতিহাস সাক্ষী কোন শইরো শাসক ওই থাকতে পারে নাই আওয়ামী লীগের ও খোব করুন ভাবে দেশ ছারতে হবে ইনশাআল্লাহ?,0,politics
আল্লাহ আপনি সবাই হেফাজত করুন আমিন,0,politics
আল্লার শাতে টখকর দিয়ে বেহেস খানা বানাইচিলো কিন্তু দেকিতে পাসছিলো কি পারেনাই। ওরা এমনটাই ছাইতেচে কিন্তু পারবে একেবারে শেস হয়েজাবে এইগুলাই পমান করে,0,politics
তুমি হলে সবচেয়ে সাহসী ইউটিউবার,0,politics
কাউয়ার সুনাম সাহারা মরূ ভূমিতে পৌছেগেছে !,0,politics
আঃলীক নাম টি নিকৃষ্টা নাম?,0,politics
খালেদা জিয়ার সাথে একজন প্রতিবন্ধীকাউয়ার সাথে তুলনা করা ভুল সর্ব প্রথম ব্যাংক ডাকাতি করছে শেখ কামাল আটহ,0,politics
গুড,0,politics
রাস্তায় হোন্ডাচারীকে ধরে জামার বুতাম লাগায়ে দেওয়ার কথা বললেন না যে !,0,politics
কি করে মানুষ বেগম খালেদা জিয়ার সাতে কাদেরের তুলনা করে।কার সাতে কি পান্তা ভাতে গি,0,politics
দাদারা এবার বড় পদ পাবে মনে হয়,0,politics
ল,0,politics
সবচেয়ে ভালো লাগছে কাউয়ার 😬😬ভয়েস কপি। কেমনে সম্ভব??🤔🤔,0,politics
আমার প্রশ্ন কাদের সাহেব এর কি লাইসেন্স আছে নি।আর মানুষকে বিনোদন দেয়ার জন্য রাস্তায় নিজেরাই জ্যাম করে আইন লখন করছে।আর এতো গুলো গাড়ি চেইক করলো একটা ও লাইসেন্স ছাড়া পেল না।ভালোই তো আমার মনে হয় ওনি লাইসেন্স সমপরকে বুঝে না।এই খানে ছাএদের দরকার ছিলো।বাহু ভালোই তো সব গাড়িতে লাইসেন্স মনে হয় ডিজি ঢেলের উপর ডিজিঢেল দুই দিনেই হয়ে গেল সাব্বাস।,0,politics
সাংবাদিকরা কেন জিজ্ঞেস করলো না যে তাহলে নেত্র নিউজের সার্ভার ডাউন কেন করা হলো?,0,politics
আরে ধুর এইগুলা গিফট্,0,politics
শালারে পাগলে গোয়া মারছে! কাওয়ার সাথে বেগম জিয়ার তুলনা করে। শালার আবাল,0,politics
চোরের দল।,0,politics
কেমন নেতা হৈলিরে নুর। ভিপির সাথে জন ভিপি এর বিপক্ষে - জন।কেমন প্রতিনিধি বুজলাম না।প্রতিনিধির উপর হামলা করা কেমনে সম্ভব হয় তুমার পুলা পান বা সাপোর্টার কই???,0,politics
বর্তমান মোবাইলের যুগে ঘড়ির পরুই জন নাই সেখানে ঘড়ির দাম এত টাকা হলে তার মোবাইলের দাম কত হবে এবং তার কয়টা মোবাইল আছে বলবেন কি?,0,politics
যাইহোক জঙ্গিমাতা হাসিনা কিন্তু থাকবেই,0,politics
সালায় কতা বলতে পারেনা সেটা না বলে চেটা বলে,0,politics
অপু বিশ্বাস কে তো কোথাও দেখলাম না ।,0,politics
নাটক,0,politics
শেখ রেহানা পন্থী ওবায়দুল কাদের ও আউট হবে আওয়ামী লীগের সাধারণ সম্পাদক থেকে নিশ্চিত,0,politics
ওবাদুলকাদে একটা হাস্যকর।,0,politics
ওরা যতই অপকর্ম করুক বাংলাদেশে এর বিচার নাই আর কোনদিন হবেও না। এটাই আমাদের সোনার বাংলাদেশ।,0,politics
চোরি মানি লন্ডারিং ও দূর্নীতিতে চ্যাম্পিয়নের সাথে ওবায়দুল কাদেরকে তুলনা করার কি দরকার।,0,politics
কহ,0,politics
ভিডিওর জন্য ভিডিও,0,politics
ভাই এত বড় গান দিছেন ইস্টাইক আসবে তো,0,politics
মানুষ আর কত নাটক দেখবে।,0,politics
নুরু ভাইকে ধমানোর জন্য সরতারের দেশের পুলিশ বাহীনীকে ব্যবহার করেছে।,0,politics
কলেজে সারাবছর রাজনীতি চলে পড়ালেখা করে কখন??,0,politics
ওদের কাছে কি সিখার আছে দেশের এতো বড় জায়গা,0,politics
যতদিন আওয়ামী লীগ থাকবে ততদিন বাংলাদেশ গজব ছড়াতে থাকবে,0,politics
ভাই এগিয়ে যান।। আল্লাহ ভরসা।,0,politics
মিথ্যা বলার জন্য অপু উকিলের গালে দুটো জুতার বাড়ি মারো,0,politics
ধনের খবর,0,politics
এত ভদ্রতা তো একবার সুষ্ঠ নির্বাচন দিয়ে দেখনা জনগণ জুতা পিটা করে ক্ষমতা থেকে নামিয়ে দেবে।,0,politics
ছার ওআয়মিলিগ,0,politics
বলতে হবে আপনার কলিজা আছে 😍,0,politics
ভয়াবহ!!! আইডিয়াই ছিল না।,0,politics
দলদারী চিরকাল থাকবে না কবরে একদিন যেতে হবে কি হিসাব দিবেন রাতে শুয়ে একবার ভাবুন,0,politics
অপু উকিল মূ্র্খ মহিলা!,0,politics
নিজের ব্যবসার জন্য একজন মানুষকে নিয়ে এতো বড়ো মিথ্যা কথা বলতে লজ্জা লাগেনা আপনার নাকি কাঁচা গাঞ্জা খান কোনটা এইসব বাদ দিয়ে পারলে দেশের জন্য মানুষের জন্য কিছু করেন,0,politics
সালারা শুধু মুখে বড় কথা বলে।বাস্তবে সভ চোর। এই চোর সালাদের জন্যই কি দেশ সাধীন হয়েছে? এই চোরাদের জন্যই দেশে এখনো মানুষ না খেয়ে থাকতে হয়। এদের দেশপ্রেম বলতে বাস্তবে সভ উল্টো।,0,politics
কি বলে ওয়া ওয়ে ওয়া আগে নুন খান!! পরে গলা পরিষ্কার করেন!!,0,politics
স্বাধীনতা পরবর্তীকালে জিয়ার বিভিন্ন অপতৎপরতায় বিরক্ত হয়ে সরকার তাকে সেনাবাহিনী থেকে সরিয়ে জার্মানীতে রাষ্ট্রদুত করে পাঠানোর সিদ্ধান্ত নেয় এর জুলাইয়ে। আক্ষরিক অর্থেই বঙ্গবন্ধুর পায়ে পড়ে কান্নাকাটি করে জিয়া এ সিদ্ধান্ত বদলের জন্য অনুরোধ করে বঙ্গবন্ধুকে। জিয়া কুর্‌আন নিয়ে কসম করে যে সে আর কখনো কোনো অপকর্মে লিপ্ত হবে না। সিংহহৃদয় বঙ্গবন্ধু জিয়াকে সেনাবাহিনীতে রেখে দেন। সেই বঙ্গবন্ধুকেই খুন করে কুট কৌশলে ক্ষমতা দখল করে মুনাফিক জিয়া পলাশীর মীরজাফর হয়ে।,0,politics
কাদের কাকু ভালো লোক ফুলের মালা তারি হক,0,politics
নুরু বাঘের বাচ্চা,0,politics
ভাই আপনার হাতে একটা ব্রেসলেট কোথায় আপনার ডান হাতে ছিলো। সেটা আপনাকে মানিয়েছিলো ভালো।,0,politics
ওবায়দুল কাদের সাথে কেমন করে খালেদার মত খুনি আগুন সন্তাসি হাওয়া ভবন বারের বিশ্ব চ্যাপিয়ান দূরনিতিতে সবার উপরে ট পাশ মূর্খ ।।কাদের খালেদার মত হয় কি করে।।মিডিয়াতে চাপা মারলে সব কিছু ঢাকা জায়না কি ছিল মেজর জিয়ার মানুষ সব জানে মাএ দুই বার খমতা এসে বিলিয়ন টাকার মালিক তারেক্কা চোর।।।,0,politics
ডিমলীগের যন্ত্রনায় থেকে বাচায় উপায় নাই,0,politics
কিছু হবে না।,0,politics
তার শ্বশুর নিশ্চয় জমিদার ছিলেন নইলে এসব ঘড়ি দেশ বিক্রির টাকায় কেনা।,0,politics
ত্ররা কি পরতে আসলো নাকি নাটক করে তোমরা ভালা অবিনয় করতে পার,0,politics
আপনাকে অনেক ধন্যবাদ আপা,0,politics
হা হা হা বেগম জিয়ার সাথে কা দি রা ভাইয়া রে তুলনা করে 😆😆😆😆😆,0,politics
শুভ জম্নদিন পূণিমা,0,politics
কথা ঠিক আছে সাহেদ ভাই,0,politics
মন্ত্রী সাহেব এখন ও মেয়েদের সাথে সেল্পি উঠাতে ভুলেন না! যদি ও উনি এখন ও অসুস্থ্য ?,0,politics
চলিতেছে সার্কাস,0,politics
হাস্যকর,0,politics
নিজেদের নোংড়া চেহারায় এরা যে একদিন দেশের মানুষের সামনে হাজির হবে তাতো জানাই ছিল । ক্ষমতালোভী এবং দুর্নিতীবাজ দালাল । বাম নামের কলংক এরা,0,politics
অপু উকিল এর কথা শুুনলে হাসি পায়,0,politics
মোনাফেকরা আজ হোক কাল বিলীন হবেই। মোস্তাক হয়েছে সাহা আজিজ হয়েছে জিয়া হয়েছে। খালেদা ও তারেক জিয়াও হবে। কারন রাজনিতীতে ষঢ়যন্ত্র কোনদিন তামাদি হয় না । এ হোল ইতিহাসের নিরব বিধান।,0,politics
ইনু এখন টিকটিকি মতো কথা বলছেন আদা পয়সা মালিক না পয়সা সাথে সুর মিলে কথা বলছে জার বিয়ের তার খবর নেই পারা পিসি ঘুম নেই,0,politics
বাগের বাচ্চা রা,0,politics
ভাই এখনই সময় হাতে হাতে ধরে দারানোর আর নয় দেরি।ভিপি নূর বলো কোথায় কিভাবে অবস্থান নিতে হবে।জেগে ওঠো বাঙালি জেগে ওঠো সকল ছাত্র সমাজ।,0,politics
কিতা কইতাম !!! সকলেরই তো কিছু না কিছু হক্ক আছে তাইনা!!!,0,politics
মিয়ানমারের মতো মিলিটারি ডিক্টেটরের দেশের মানুষও পাবজি খেলতে পারে। মিয়ানমার কনসারভেটিভ রাষ্ট্র। আর আমরা বাংলাদেশ রিপাবলিক দেশ হওয়ার পরও আমরা পাবজি খেলতে পারি না। পাব্জি কানেকশন ব্লক করে দেওয়া হয়েছে। আমি সফটওয়্যার ইঞ্জিনিয়ার নই তাই আমি বলতে পারবো না আসলে কি করা হয়েছে কিন্তু সাধারণ হিসেবে এটা বুঝি যখন একটি নিরদিষ্ট টেকনিকে ঢুকতে হতো তখনও ব্লক করা হয়েছিল কিন্তু ঠিক মতো করতে পারে নাই কিন্তু এবার এমনভাবে ব্লক করেছে যে আপনি ভিপিএন কানেক্ট না করে যেভাবেই ঢুকেন আপনি ভয়েস চ্যাট করতে পারবেন না। পাবজি খেলতে দিবেন না ভাল কথা কিন্তু এটা এত লুকোচুরির কি আছে ডাইরেক্ট ব্যান করে দিলেই পারতেন কিন্তু তা না করে করলেন ব্লক ব্লক করার পর অফিসিয়ালি একটা স্টেটমেন্টও তো দিতে পারতেন কিন্তু তাও না করে চোরের মতো চুপ করে আছেন। আমাদের কি কোন দাম নাই যে অফিসিয়ালি একটা স্টেটমেন্ট দেওয়ার প্রয়োজনীয়তাও মনে করলেন না আপনারা? পৃথিবীতে পাবজি খেলে না কোন কোন দেশ? উত্তর কোরিয়া। আর খেলে কোন কোন দেশ? যুক্তরাষ্ট্র রাশিয়া সোউদি আরব জাপানসহ বাকি সব দেশ। আপনারা যুক্তরাষ্ট্রকে অনুসরণ না করে অনুসরন করছেন উত্তর কোরিয়াকে। বাহঃ তালি হবে👏। জানি পাবজি খেলা উপকার নাকি অপকার সেই ডিবেট এখন নিয়ে আসবেন। আমি সিম্পল মানুষ সবকিছু সিম্পলভাবেই বুঝি। পাবজি খেলা যদি খারাপই হতো তাহলে ম বিশ্বের কান্ট্রিগুলো সবার আগে ব্যান করতো। জাপান পৃথিবীর সবচেয়ে শান্তিপ্রিয় দেশ জাপান যেহেতু ব্যান করে নাই আপনারা ব্যান করার কোন যৌক্তিকতা নাই। আপনারা হয়তো পাবজির বিরুদ্ধে নানান যুক্তি দিতে আসবেন কিন্তু যখন বাস্তবিক উদাহরণই আপনার সামনে আছে তখন যুক্তি দেওয়া অর্থহীন। যারা সবার আগে আনে যাদের থেকে আমরা বছর পিছিয়ে যারা ম বিশ্ব তারা আপনাদের চেয়ে কম বুঝে না। তারা পাবজি ব্যান করে নাই। আপনারা কথায় কথায় ডিজিটাল বাংলাদেশের কথা বলেন গেমিং হল খেলাধুলার ডিজিটাল প্লাটফর্ম সেটাই এখন আপনারা বন্ধ করে দিলেন। এরকম অনেকেই অনেক স্টযাটাস দিয়েছে কিন্তু কোন লাভ হচ্ছে না তারা চুপ করে নীরবে বসে বসে হাসছে। আমরা আমাদের প্রিয় গেইম খেলতে চাই এটা আমার অধিকার আমার টাকার স্মার্টফোন আমার টাকার সিম আমার টাকার এমবি কোন গেইম খেলবো আমার চয়েজ। আমার চয়েজে অন্যের চয়েজ চাপিয়ে দেওয়ার মানে আমার অধিকার হনন করা। স্টযাটাস দিয়েও যখন তাদের দৃষ্টি আকর্ষণ করা যাচ্ছে না সুতরাং অন্যকিছু করতে হবে পাবজি লাভার সবাই অথোরিটির অফিসে যাব। কেউ একটা ইভেন্ট খুলেন। এখন কিছু প্রানী এসে বলবে আমাদের দেশের অথোরিটি পাবজি ব্লক করে নি। তাদেরকে বলে রাখি পাবজি কোন ছোটখাটো প্রতিষ্ঠান না যে সারভারের সমস্যা এতোদিন থাকবে। তাছাড়া পাবজি আপনার মতো বেকুব না যে আমাদের কোটি মানুষের মার্কেটে হাজার হাজার গেমার যারা কিনে তাদেরকে এভাবে বসিয়ে রেখে এতোগুলো কাস্টমার লস করবে। যদি পাবজির পক্ষ থেকে কোন সমস্যা হতোই তবে তা এক দুইদিনের মধ্যে ঠিক করে ফেলতো তাদের ব্যাবসায়িক সার্থেই। বাংলাদেশের অথোরিটি থেকে ব্লক করলে পাবজির বাপেও তো কিছু করতে পারবে না। আমরা যদি আবার আমাদের প্রিয় গেইম খেলতে চাই আমাদের পক্ষ থেকে যা কিছু করা সম্ভব তা করা উচিত। ইভেন্ট খুলেন তারিখ দেন আমরা পাবজি লাভার সবাই অথোরিটির কাছে যাব। ?,0,politics
তোকে ছাড়া সুন্দর চলবে,0,politics
এই দেশে সবচেয়ে বেশি টাকা খরচ হয় রোডস এন্ড হাইওয়ে। আর সেই মন্ত্রণালয়ের মন্ত্রী তিনি বুঝতে হবে আপনাকে।।।,0,politics
শুটিং চলছে নাকি এত্তো ক্যামেরা ক্যান?,0,politics
রুমি আপা আপনার অনেক তেজ। আপনাকে একটু করা যাবে ভিজিট কত করে।,0,politics
টিপওয়ালি ডেটা ওয়ান নামবার বেয়াদব।,0,politics
জনগনের হোগা মারা শেস।,0,politics
রুমিন ফারহানার একটা নখের যোগ্যতাও অপু উকিলের নাই।,0,politics
নুর ভালো লোক।।। এই সরকারের কাছে উছিত কথার দাম কেও পাবে না কারণ এখন দেশ চলে চাদা বাজি করে দূনীতি বাজি করে নুর উচিত কথা বলছে বলে তার সাতে আজ এতো অত্তচার করা হচ্ছে বাংলাদেশের মানুষ হয়তো ভুজছে না কিন্তু ভুজবে।।।। বাংলাদেশ এখন আগের দেশ নেই চোরের দেশ গিনা হয় এই দেশ কে।।।,0,politics
কোন একদিন শুনাযাবে ভিপি নুর ও গুম হয়ে গেছে।,0,politics
🕋🌹আল্লাহ মাফ করুক।🌹🕋 🌏সকলকে আন্তরিক অভিনন্দন।🌷 আমাদের চ্যানেলটি সাবস্ক্রাইব করুন।,0,politics
এই সরকার এর পতন চাই👈👍,0,politics
কিভাবে তুলনা করে এরা কার সাথে কার তুলনা করে,0,politics
খালেদা জিয়ার সাথে ওবায়দুল কাদেরের তুলনা এটা আমাদের জন্যো একটা হাইশকর হাইসকর,0,politics
এখন সসম্ভবত হিন্দু কাউকে দিবে,0,politics
অাওমিলিকের রাজনৈতিক নেতা বলে কখা।।।।অনেক দিনের শখ,0,politics
ভাই আপনি কি নামাজ পড়েন খুব জানতে ইচ্ছে করছে শুক্রবার দিনেও কি পড়েন জুম্মার নামাজ,0,politics
এই সেই ওবায়দুল কাদের যিনি কয়েকদিন আগে খেটে খাওয়া রিকশাওয়ালাদের অপমান করেছেন।,0,politics
সালা চোর মিথ্থা‌,0,politics
ভাই চুল গুলা জোস,0,politics
এ ভাই ওবায়দুল কাদেরকে এক গ্লাস মুলার জুস দে,0,politics
মামা তোমার দাঁড়ি মুছ ঠিক কর আগে,0,politics
সব বাদ দিয়া ইন্ডিয়া আর কথা শুইনা হিন্দু ধর্মের লোক ঢুকাইবো 😅,0,politics
মাঝে মাঝে ‌আপনাকে দেখি মিডিয়া নিয়ে রাস্তায় এই ফাটাকেষ্টর ভুমিকায় কাদের সাহেব শুনেন মানুষ রে আর বোকা সাজাবেন না |এই লোক দেখানো দ্বায়িত্ব না দেখিয়ে সত্যিকার অর্থে কিছু করার চেষ্টা করেন !!,0,politics
কে বলে রে দেশ স্বাধীন হয়েছে,0,politics
সব চোর হাসিনা দল হাসিনা হল ভোট চোর,0,politics
ভাল লাগল ভাই আপনার আলোচনা,0,politics
বেগম জিয়ার সাথে কাউয়া কাদেরের কোন তুলনা হতে পারে!,0,politics
আছি ভাই আপনার সাথে❤❤❤❤,0,politics
ভাই এইসব তাদের কোনো শালাদের কানে যাবে না।,0,politics
তুমি যা দেখাও তুমি তো বাংলাদেশ যা সব ইউটিওবার পারেনা হাজার সালাম বস তমাকে,0,politics
লীগ এখন হীরক রাজার দল। পরিবর্তন হলে ও কি আর না হলে ও কি। মানুষের মাঝে কি আনন্দ আছে। বিনা ভোটে ভারত ও দেশের সরকারি বাহিনীর উপর ভর করে সরকসরে আছে।,0,politics
সুলা সুলি লাগ বইন আমরা আসি দেখতেসি। 😁😇😁😇😁 উবাইদুল কি পারবে পেটে সন্তান জন্ম দিতে 😇😁😇😁 সবয় সমান একটা কাক আর একটা পেছা 😁😇😁😭😀😀😩,0,politics
আমাদের পান পিও কাউয়া কাদের,0,politics
ধের বোকা া অংশ মানুষ তিন বেলা খেতে পারে না।পাগোল করো বাইন দ,0,politics
উন‍্যয়ন ঠিকই করেছে তবে দেশের মানুষের নয় নিজেদের,0,politics
কই লিভারপুল আর কই ফকিরাপুল 🖕,0,politics
কই কাক আর কই কোকিল হালা মদ খা তর মাথায় গ্যাষ্টিক আছে কাওয়া ত একটা চোর।,0,politics
নতুন বছরের তর নাম দিলাম বাইলা হাঁস তুই আর পেক পেক করিস না জনগণের ভোটাধিকার হাইজ্যাক করে ক্ষমতায় টিকে কত দিন থাকবি সময় এক দিন ফুরিয়ে যাবে।,0,politics
স্যার তো হাসছে এসব স্যার জুতা মার । ছাত্রলীগের বিরুদ্ধে কঠোর আন্দোলন গরে তোল মারের বদলে মার,0,politics
অাপনাকে অনেক ধন্যবাদ ভাই জান,0,politics
সালা,0,politics
অাল্লাহর সামনে দারাতে হবে মনে রাখিস চোরেরা।,0,politics
সবই থাকবে তুই থাকবি না। তাই ভালো খয়ে জাও।অবয়দো ভাবে খমতাই এসে কি লাভ।,0,politics
বেগম খালেদা জিয়ার প্রসাধনী সামগ্রী পরচুলা ও শাড়ী দাম কতো? খালেদা জিয়ার বিলাসবহুল জীবনযাপন নিয়ে কথা বলুন? নিরপেক্ষ থাকুন যদিও আপনারা নিরপেক্ষ থাকার ঢং করেন বিশেষ কিছু গোষ্ঠীর স্বার্থে ভিডিও বানান হয়তো এটাই আপনাদের মূল জীবিকা যদি তা না হয়ে থাকে তবে খালেদা জিয়া ও তারেক রহমানের বিলাসবহুল জীবনযাপন নিয়ে ভিডিও বানান ধন্যবাদ।,0,politics
ভাই আপনি একটা জিনিস গোলা নকল টা ভাল লাগছে 😍😍,0,politics
কাদেরে জুতা টানার জন্য রাখবে খালেদা জিয়া,0,politics
বছর পর লাইক দিলাম। আশাকরী ডিসেম্বর এর আগের শাহেদ আলম ভাই কে পাব,0,politics
সব বড় ব্যবসায়ীরা এসব গিফট দেয় মন্ত্রীদের হাত করার জন্য,0,politics
চুরের রাজনীতি,0,politics
গুলিস্তানের কপি মাল।,0,politics
আপনকে ধন্যবাদ,0,politics
সরকারের কাছে একটা ছাএলিগ কে বরিসকা করা হোক,0,politics
নষ্ট,0,politics
খালেদা চোর একিমের টাকা মেরেদিয়েছে খালেদা খারাপ মানুষ,0,politics
ভালো লাগে আপনার প্রতিটা ভিডিও এটাও তার ব্যাতিক্রম না আপনি এবং ইলিয়াস ভাইয়ের মতো ইউটিউবার অনেক কম আছে আপনাদের ভিতর একজন জাগরিত নাগরিকের পরিচয় আছে,0,politics
য় বেটি কাউয়া কী তোর জামায় লাগে নি?,0,politics
ছাত্রলীগ দেখতে অবিকল মানুষের মত। 🐖 🗡ছি 🗡ছি🗡 ছি 🗡ছি🗡🐖,0,politics
সাউন্ড কোয়ালিটি ডাউন।,0,politics
না অনাকে দেশ ও দলের জন্য থাকা দরকার,0,politics
ভিপি নূর সহ এইখানে যারা বগর বগর করে । তাদেরকে এইভাবে লাথি গুতা না মেরে সরাসরি মেরে ফেলেই তো হয় । শালা সরকার বিরোধী একটাকেও রাখা উচিত না,0,politics
খালেদা জিয়া ভোট চুরি করে জিতেছিল যে ভাবে এতিমের টাকা চুরি করেছে,0,politics
সালা কাউআকে জুতা মারা দরকার,0,politics
ভাই আপনার ভিডিওতে বকবক বেশি করেন তাই আপনার ভিডিও দেখি না।তাছাড়া আপনি একজন নেগেটিভ মানুষ।,0,politics
ইট মারলে পাটকেল মারো,0,politics
ওবাইদুল কাদেরের ঘড়িগুলা হয়ত নকল😀😀। ডুবাইতে বাংলাদেশি হাজার টাকায় এমন ঘড়ি হুবুহু পাওয়া যায়।,0,politics
আলু বাবার চল্লিশ চোর 😆😆,0,politics
নূর তুমিই বাঙলাদেশে,0,politics
এ তো কথায় বলতে পারে না,0,politics
কখনও বেগম খালেদা জিয়ার সাথে কাদেরের তুলনা চলবে না। খালেদা জিয়ার মতো জনপ্রিয় মানুষ বাংলাদেশে আর নেই। এমনকি মুজিবও না। কোথায় লিয়াকত আলী আর কোথায় জুতার কালী। লজ্জা হওয়া উচিৎ আওয়ামী রাজাকারদের।,0,politics
আলহামদুলিল্লাহ,0,politics
বাংলাদেশ এ ভালো মানুষের কোন মুল্য নেই।,0,politics
খুব সুন্দর ভাবে ভিডিও টি সাজিয়ে উপস্থাপন করেছেন ভাইয়া💝✌ নেক্সট আপলোড এর অপেক্ষায় রইলাম ভাইয়া💝💝💘💘,0,politics
আওয়ামীলীগ মানেই গাজা খোর 🐕,0,politics
ও একটা পাগল,0,politics
শিক্ষক পুরাটাই দালাল শিক্ষক সন্তাশিকে পছরয় দিয়া বেরায়,0,politics
আওয়ামিলীগ এর পক্ষের ওই ম্যাম কি বলে এইসব,0,politics
কাউয়া হালায় করে কি তোর নাটকে মুগ্ধ জাতি,0,politics
খালেদা জিয়ার মুক্তি চাই ✊✊,0,politics
সাহস! 😱,0,politics
আমি এক জন নগুরীক হিসাবে জানতে চাই একাতুরের জেবাবে রুখে ছিল আমাদের জোদা সেই একই বাবে দারাতে হবে না না না আর বসে থাকবেন না,0,politics
এই সব পম্দাসেতুর টাকা ‌। ফখরুদ্দিনের আমলে যেভাবে সবার হিসেব নেয়া হয়েছে ঐভাবে হিসেব নিলেই সব চোর ধরা পড়ে যাবে সব চোর,0,politics
কাওয়া গদি ছারলে বুজবে জুতা কেমনে খায়,0,politics
ভাই অপনার সাথে মিনিট কথা বলতে চাই,0,politics
কাদেৱ তো ঠিক ঠাক বাংলা বলতেই পাৱেনা ।। কাৱ সাথে কাৱ তোলনা কৱে বাংলাৱ বুকাৱা,0,politics
দুর হালা,0,politics
এইগুলা মেয়েরা হাদিয়া দিয়েছে,0,politics
বিএনপি যতবার ক্ষমতায় এসেছে ষরযন্ত্রের মাধ্যমে এসেছে😆😆😆,0,politics
প্রতিবন্ধী মন্ত্রী,0,politics
জিয়া,0,politics
অসাধারণ বিনোদন পাইলাম ভাই,0,politics
সত্যি কথা আল্লাহ আর আল্লাহর রাসুল পছন্দ করেন তোমরা মিথ্যা কথা বলিওনা মনে রেখো এক দিন সবাইকে মরতে হবে !!!,0,politics
টাকার অভাবে তো ঘড়ি কিনতেই পারলাম না।,0,politics
ডিম লীগ হাতুড়ি লীগ থেকে দেশকে মুক্ত করতে হবে।,0,politics
কুটায় গরু চুর আর কুটায় বারের পদান,0,politics
জনগনের টাকা চুরি করে খালেদাজিয়া। কাদের সাহেব করে জনগণের সেবা।,0,politics
টাইটেল দেখে ভাবছিলাম নতুন নিউজ কিন্তু না দেখি আগের টাই নতুন করে,0,politics
নুরা শিবির,0,politics
ভাই আপনি বাংলাদেশে থাকেন,0,politics
সালা কাউয়া মিথ্যাবাদি,0,politics
কা কা কা কই খালেদা কই ওবায়েদা,0,politics
হাজার বছরের জন্য সমজতা করার কি দরকার তোরা তোদের দলকে বিলুপ্ত করে অাওয়ামীলিগে যোগদান করলেই তো পারিস হালা গাদা।,0,politics
আওয়ামী লীগের অভ্যন্তরীণ গণতন্ত্র নেই। কেন একজন মানুষ আটবার ধরে সভাপতি হচ্ছে?? আর কি কোনো যোগ্য লোক নেই??,0,politics
বাংলাদেশের বড় চোর নামে খেত কাদের।ওই আওয়ামী লীগের মাটিতে মিলানোর কাজটা করছে।কাদের হল বিশ্ববাটপার।,0,politics
বলদেরা কি সব প্রশ্ন করে কই ওবাইদুল,0,politics
আমার মনে হয় শিক্ষক পাইখানা খেয়েছে।,0,politics
সঠিক বলেছেন আপু,0,politics
কাউয়ারে কাউয়া কইত ন কি বাল নি কইব হালা চামচিকা,0,politics
এক চোর আরেক জনকে বলে কত টাকা আয়,0,politics
আওমীলিগ এবার বার জামানত বাজেআপত বার জামানত ফেরত বার নৌকার বাড়া ভাত খেয়ে এম পি হাসানুল হক ইনুকে কি ফাঁসি দিবে।,0,politics
আওয়ামীলীগ করে এখনো কথা বলতে জানেনা কি করে কথা বলবে মিথ্যে কথা বললে কথা তো এমনিই আঁটকে যাবে কারণ আওয়ামীলীগ বলতেই মিথ্যে বাদী,0,politics
অসাধারণ ছিলো ভাইয়া👌,0,politics
তোদের নেত্রী জানে যদি খমতা ছেঁড়ে দেই তাহলে দেশের জনগণ আমাদের কে ছাড়বে না ?,0,politics
কি ভাই ভারতে যান নাই দালালের দালাল,0,politics
ইনু চাচা ভোটার বিহিন নির্বাচন হলে তো সাধীন বাংলাদেশ হবে ।আর সাধীন নতার সাধ জাগে উঠবে জনগণের মধ্যে ইন শাললা।,0,politics
প্রথম বক্তার বক্তব্য শুনে আবেগে কেঁদেয় ফেলবো প্রায় অবস্থা আমার।,0,politics
হাজারিকে চাই,0,politics
কাদের কে খালেদা জিয়া পিয়ন হয়ার যোগ্যতা নেই,0,politics
ভ।ই এগুলো বলে ল।ভ ন।ই কিছুই হবে ন। যেহেতু আওয়।মীলিক এখন সরক।রে আছেন,0,politics
স্বামীর মৃত্যুোর করুনায় একজন কিচেন রুমের রাঁধুনী সাথে রাজপথের লড়াকু সৈনিক ছাত্র রাজনিতীর ধারক বাহক ষাটের দশকের অান্দোলন সংগ্রামে অগ্রনী ভূমিকা প্রতিটি স্তরে স্তরে সাফাল্যের বীর সৈনিক সবচেয়ে মানুষের প্রিয় প্রানের দলের সেকেন্ড ইন কমান্ডকে তুলনা করে জাতিকে লজ্জিত করার কি দরকার ছিলো।,0,politics
ওবায়দুল কাদেরের সাথে খালেদা জিয়ার সাথে কোন তুলনা নেই ওবায়দুল কাদের সড়ক মন্ত্রী আর খালেদা জিয়া সে দেশের একজন নেত্রী,0,politics
নুর ছেলেদের হ লে গেছে সেটা ঠিক আছে কিন্তু মেয়েরা ছেলেদের হ লে কি করে?,0,politics
তিন বারের প্রধান্মন্ত্রি এক ইউনিট বিদু্্যত উৎপাদন করতে পারে নাই।,0,politics
বেগম জিয়ার সঙ্গে ভোট চোরে তুলনা হাস্যকর ব্যাপার,0,politics
যে সরকারই আসে সেই লুটপাট করে আওমীলিক লুটপাট করছে করুক ক্ষমতায় থাকতে চায় থাকুক কিন্তু দেশটাকে যে ভারতের কাছে বিক্রি করে দিচ্ছে এখানেই অনেক ভয় কাজ করছে কবে যেন বলে ফেলে গরুর গোসত খাওয়া যাবে না খাইলেই মামলা আর জেল,0,politics
আবার হাডএটাক্ট করবে কাউয়া,0,politics
গাজা খাইছে 😂😂😂😂,0,politics
অপু মহিলা কি বাজে,0,politics
যে দেশে হাজার কোটি ডলার রিজার্ভ চুরি হয়।সে দেশের মন্ত্রী কোটি টাকার ঘড়ি পরবেন।এটা খুব সাধারন ব্যাপার নয় কি !,0,politics
পুরা চোরের দলকে মনে রাখবে।,0,politics
কেউ যদি নিজের বেতন দিয়ে লাখ টাকার ঘড়ি কেনে আমার তাতে কোনও সমস্যা নাই। সমস্যা সেখানে যদি সেটা নিজের বেতনের টাকা না হয়। আর যে লোকটা গিফট দিল তার সে কি নিজের বেতন থেকে দিল?,0,politics
সড়ক মন্ত্রী রাস্তায় নামতে হয় কেন? ওনার কি লোকজন ওনার কথা শুনেন না? হাই কমান্ডেদের যদি এই অবস্থা হয় তাহলে দেশ চলবে কি করে? দেশ যে কিভাবে চলছে তা তো আমরা দেখছি।,0,politics
অপু দিদি আর সন্ত্রাসী লিগরা ইউ টুবের কমেন্টস গুলি দেখেনা মনে হয় দেখলে আজে বাজে কথা বলত না,0,politics
ভিসির পদোতেক চাই,0,politics
চেহারা দেখেই চোর চিনা যায়😃,0,politics
অসাধারণ অসাধারণ তুলনা হয়না আমি আপনাকে সেলুট জানাই,0,politics
অপু ম্যাডাম ঠেলা কথা আর কত বলবেন মানুষ বুঝে।,0,politics
শান্তুনু কায়সার আপনাকে ধন্যবাদ!!!,0,politics
জনাব কাদের সাহেবকে নিয়া কোন কথা নাই।তবে বাংলাদেশের মানুষ নিয়ে যে কথা বলেছেন সেটা নিয়ে আপত্তি আছে।বাংলাদেশের মানুষ এখন সবাই তিন বেলা ভাল করে খেতে পারেন এখন মন্ঙ্গা নেই দেশের মানুষকে নিয়া ছোট করে দেখার অধিকার আপনার নাই।,0,politics
ম্যাডাম সত্যি কথা কখনো মুখে বাজেনা আর আপনার মুখতো থোতলামিতে গ্রেট পেয়েছে। আর ওবায়দুল কাদেরের আর এক জন প্রধান মন্তি তুলনা কখনো যায় না। ওবায়দুল কাদেরের তুলনা সুদু হিরো আলোমের সাথে দেয়া যায়।,0,politics
এসব নাটক জনগন অার পছন্দ করেনা।,0,politics
আপনী কি কাদের হতে জেনেছেন?? এভা মানুষকে হেয় করা আপনারই কাজ দেশে আশুন জবাব চান,0,politics
আগুন নুরু আর তোদের মাথার উপর জ্বালা,0,politics
চোরের মার বড় গলা,0,politics
আওয়ামী লীগ কে ফিল্টার করো,0,politics
অপু কে জুতা মারলে জুতার ইজ্জত যাবে,0,politics
মিথ্যা কথা বললে মুখে এভাবেই কথা আটকে যায়। অপু উকিল ছেঁচড়া,0,politics
ওবায়দুল কাদের মাসে মাসে গেম খেলে নাইকাদের সাথে,0,politics
হা হা বাংলা দেশ,0,politics
আমি তার এলাকার লোক হিসিবে বলছি নেতা হতে আসেনি মানুষের সেবন করতে এসেছি আগে যেখানে সেবক ছিল,0,politics
বাড়ি নাই ভাড়া আসে কোথা থেকে,0,politics
আমরা কমেন্টে দেখব কার জনপ্রিয়তা বেশি।,0,politics
মেয়েতো নয় মনে হচ্চে,0,politics
এগোলো কে কি বলবো,0,politics
একটা ঘড়ির দাম দিয়ে আমাদের মত মানুষের জীবন পালটে যাবে,0,politics
কিছুদিন আগে ছিল হেলমেট লীগ। এখন বের হইছে ডিম লীগ।হায়রে বাংলাদেশ,0,politics
ওবায়দুল কাদেরের সাথে খালেদা শেখ হাসিনার তুলনা চলে না,0,politics
বোনগো আপনি কি জানেন খালাদা। জিয়ার জন্ম তারিখ বার।,0,politics
ভাই আপনাকে স্যালুট। হাজারো নাগরিক এর জমিয়ে থাকা কথা গুলোই আপনি প্রকাশ করেছেন,0,politics
কাউয়া আর দেশ মা খালেদা,0,politics
ইনু কে বাদ দেন,0,politics
জাগ জনতা জাগ দেশ প্রেম তারা বাট পারি,0,politics
এসব সন্ত্রাসীদের ধরে ধরে গুলি করে মারা উচিত কারণ ওদের দিয়ে বাংলাদেশের খারাপ ছাড়া কখনো ভালো হবে না। কিছু দালাল আছে যাদের আমার কমেন্ট পছন্দ হবে না। তাদের উদ্দেশ্যে বলছি তোমাদের কি করার আছে থাকলে আমাকে করতে পারো সালা জারজ সন্তান সবগুলা।,0,politics
এই পাকিস্তানপন্থিটা বলে কি? ও আবার ওবায়দুল কাদেরকে বলে সাধারণ সড়ক মন্ত্রী 🤔 দু টাকার সাংবাদিক 😑,0,politics
হারাম কা মাল ধরিয়া মে ডাল,0,politics
কই আগর তলা আর কই ওগার তলা কার সাথে কি পান্তা ভাতে কি খালেদার সাথে কাদেরের তুলনা হাসতে হাসতে পেটে ব্যাথা করতেছে অপুর কথা শুনে,0,politics
আহম মুস্তাফা কামাল কুমিল্লা কুমিল্লার রোড,0,politics
বহিরাগত কোনও ছাএ হোস্টেলে বা বিশ্ববিদ্যালয়ে কেনও থাকবে তাদের লাথি দিয়ে বের করে দাউ,0,politics
এই অবোইদো মনতি আর নাটক কইরেন না জাতি ভালমতো বুজে এসব নাটক,0,politics
বাংলাদেশের ভিতরে আল্লাহর গজব পড়ছে গজব আল্লাহ তুমি আমাদেরকে সবাইকে রক্ষা করে গজবের থেকে,0,politics
বোনের রাজার সিংহের সাথে গ্রামের কুকুরের তুলনা,0,politics
আল্লাহ নুর ভাইকে হেফাজত করো আমিন,0,politics
কোথায় মানবতা !,0,politics
জে গুলি চোর খারাপ বেয়াদব এগুলি আমাদের বাংলা প্রিয় নেতা ওবায়দুল কাদের সাহেব কে বাঁজে কতা বলে,0,politics
কবে জানি শুনতে হয় নুরু আর নাই😭😭😭😭,0,politics
সাল থেকে আওয়ামী লীগ নিরপেক্ষ নির্বাচন দেয়নি কেন কারণ আওয়ামী লীগের ডাকে জনগণ সাড়া দেয় না ভোট কারচুপি তো আওয়ামী লীগের জাতিগত পেশা এখন বেগম জিয়ার সাথে কাউয়া মন্ত্রী তুলনা করে একেই বলে ছাগললীগ,0,politics
কাক যতই তেরিবেরি করোক না কেন কখনো ময়ূর হতে পারে না,0,politics
খালেদাজিয়ার শাড়ীর কালেকশন গুলা এখন কোথায়??,0,politics
বেগম জি যার পশম ও না কাউযা,0,politics
কোথায় আগলতলা কোথায় খাটের তলা কিসের সাথে কিসের তুলনা করে 😂😂😂😂,0,politics
মিথ্যা নিউজ।,0,politics
টিক বলেছেন,0,politics
ইনু তোকে বলছি টিসু পেপার একবার ই ব্যাবহার করা যায় দুই বার নয়।।।।।।।।,0,politics
ডিম লীগ,0,politics
ভাই আপনার ঘড়িটা আর আমারটা সেইম,0,politics
অনেক ধন্যবাদ রুমিন ফারহানা,0,politics
এই হালার পোয়া দেশের জন্য এভাবে রাস্তায় হাটেনা সে নিজের জন্য হাটে কারন সে ডায়বেটিস রোগী,0,politics
এই ঝিনুকে আবারও চৌদ্দ দলে রাখলে মহাপ্রলয় হবে শাপকে বিশ্বাস করতেনেই।,0,politics
দেশের কথা বলছে এরাই তো বাংলাদেশ যারা বলে আমরা শেখ মুজিবের সৈনিক তারা তাদের সমাজে শেখ মুজিবরের মতো কত জনের উপকার করেছে এরা দল ও দেশ লুটে খাওয়ার জন্যই মুখে এ কথাটা বলে আমরা মজিবের সৈনিক বা জিয়ার সৈনিক মুখে না বলে কাজে প্রমান কর যে তোমরা মুজিব বা জিয়ার সৈনিক যাতে মানুষ বলতে বাধ্য হয় হুম এদের মাঝে মুজিব বা জিয়ার আদর্শ আছে?,0,politics
আপনি তো নিজেই অনুপ্রবেশকারী,0,politics
কাউয়ার ভাত মরছে,0,politics
এই গোলা এডেটি করা জাই ভাই😃😃😃😃😃😁😁😁😁😁😁😁😁😁,0,politics
ভাই খুব সুন্দর,0,politics
আপনারা যাই বলেন শাহেদ ভাই সবসময় যুক্তি সঙ্গত ভিডিও তৈরি করেন। সত্য তথ্য নির্ভর,0,politics
অপু উকিল একটা বড় ভোট ডাকাত আমার আসনে ভোট ডাকাতি করে ক্ষমতা এসেছে তার স্বামী আমি তার প্রমাণ তার মুখ দিয়ে ভোটের কথা শুভা পায় না যদি লজ্জা থাকতো তাহলে কথা বলতো না। হারামির বাচ্ছা,0,politics
হিরো আলম এবং ওবায়দুল কাদের হাহাহা,0,politics
আপনার মতো সাহসি ইউটিউবার কম ই আছে,0,politics
ও আমার মা ও বোনেরা আগে আমারদেশের ইসলাম ধর্মকে মানুন। ভিডিও হচ্ছে চলতেছে সাড়া বিশ্ব দেখবে। তো মাথায় আগে কাপড় রাখেন। ওবায়েদুল কাদের ও তো দেশের কুলাংগারের দলের একজন চাম বিছা কই দেশের একজন শহীদ প্রেসিডেন্টর জিয়াউর রহমানের স্ত্রী আর কই কুলাংগারের দলের একজন গুখোড়। অপু তো চালার আপনি তো মুসলমান তো অপুর সাথে আপনার অনেক ব্যবদান আছে। আপনি মুসলমান আপনাকে ইসলাম মানতে হবে। পর্দা করুন। কেমন।,0,politics
আমি বুঝিনা আওয়ামী লীগ কিভাবে এদের দলে রাখে 🤣,0,politics
জুতা পারেন খুনি লিগ কে এরা বর বর কতা আর খুন করা চারা আর কিছু না,0,politics
এতোদিন পর???,0,politics
ভাইয়া আপনি আমেরিকারতে কি করেন?? আপনি সব সময় ভিডিওতে বলেন আপনি আমেরিকাতে আছেন তবে আমার খুব জানার ইচ্ছে আপনি ওইখানে কি করেন।,0,politics
এটার মানে কি পাগলের পাগলামি দেখ,0,politics
আপনি সব সত্যি কথা বলেছেন কার মানতে কষ্ট হবে না।,0,politics
কি হবে শিক্ষা দিয়ে যদি না হয় প্রকৃত মানুষ গুলি কি হবে রাজনীতির শিখেন যদি না হয় দেশ শান্তিতে,0,politics
ভিপি নূরকে ভিতরে আটকে রেখে মারধর করা হইতাছে আর এই কুলাংগার এর বাচ্চা কইতাছে ভুল বোঝা বুঝি হয়েছে এই সমস্ত জারজ সন্তানের জন্য দেশের আজকে এই অবস্থা,0,politics
খেয়াল করেন রুম থেকে বের হল সার্ট গায়ে পরে পান্জাবী তাতে ডিম লাগা ।,0,politics
আওয়ামিলীগ জন্মগত ভাবেই কুখ্যাত মিথ্যুক কুখ্যাত নির্লজ্জ বেহায়া কুখ্যাত সন্ত্রাসী খুনি দুর্নীতিবাজ কুখ্যাত স্বৈরাচার আওয়ামিলীগ জনগণের ভাগ্য উন্নয়নে কাজ করেনা আওয়ামিলীগ কুখ্যাত সন্ত্রাসী কুখ্যাত স্বৈরাচারী দের ভাগ্য উন্নয়নে কাজ করে,0,politics
বিএনপির এই সব গুজব নেত্রী,0,politics
শাহেদ ভাই আপনি অনেকটা রাজনৈতিক ব্যক্তিদের মত কথা বললেন। 👎👎👎 ভাই যদি একটু আপনার সম্পর্কে বলতেন। আপনি কে কিভাবে এবং কেন?,0,politics
সাবান বাগের বাচ্চা,0,politics
নিশ্চই কোন হিন্দুরে বাসাইবো । যাতে ভারতের কাছে দেশটা বিক্রী করতে অসুবিধা না হয় যেমনটা রাব্বানিকে সরিয়ে এক হিন্দুকে বসাইছে,0,politics
হারাম। হারাম। হারাম।,0,politics
সতি কথা,0,politics
সালারা কাজ নাই খালি খবর আর খবর,0,politics
বাংলাদেশে ট্রাপিক পুলিশ নাই। এখন মন্ত্রী নেমেছে রোডে। আর কিছু দিন পর প্রধানমন্ত্রী ট্রাফিক পুলিশের কাজ করবেন। আর সারা দুনিয়ার মানুষ তামাশা দেখবে।,0,politics
এভাবে চললে কিছুদিন আর দুর্নীতিবাজদের ধরা যায় ।।। হায়রে কোন দেশে বাস করছি !!!,0,politics
এগিয়ে যাও ভাই ভয় পেওনা । পুরো দেশ তোমার সাথে । সত্য কথা আমাদের বলতেই হবে।,0,politics
শাহজাহান খান এর সাথে যদি কি যুক্ত হয় তবে ওবায়দুল কাদেরের নামের সাথে কি যুক্ত হতে পারে?,0,politics
এদেশের বিরুদ্ধে কথা বললে দেশ বিরুদ্ধি হয় না পাকিস্তানের পক্ষে জামাতের পক্ষে কথা বলে দেশবিরুদি হয় এর নাম বাংলাদেশ,0,politics
সারা বাংলাদেশ এখন দুই ভাগ ছাত্রলীগ আর বাংলার ছাত্র ও আপামর জনসাধারণ । এরা বিতলে গেছে।এদের হায়না এর মতো আচরণ। সালার কুত্তা লীগ।,0,politics
দেশের সচেতন নাগরিক হিসেবে আমার দাবি সন্ত্রাসি বনাম কথিত ছাত্রলীগকে সম্পুর্ন্য বাবে নিসিদ্দ করা হোক তারা দেশের সম্মান সার্বভৌমকে ধ্যংস করে দিচ্ছে ।,0,politics
সাবক্রাইবার কমে গেল নাকি??,0,politics
আমার আমাদের টাকা,0,politics
হা হা হা কাঊয়ার নাকি সুনাম !,0,politics
আমার হাতের ঘড়িটা কাদের ভাই থেকে সুুন্দর। জাপানের ঘঢ়ি।দাম টাকা।,0,politics
ইনু কে জুতা পিটা দরকার।,0,politics
শুভ কামনা প্রিয় দল আওয়ামীলীগ।,0,politics
ভাই আপনি দেশে আছেন নাকি বিদেশে।,0,politics
এতিমের টাকা মারে খেয়েছে কিনা সেটা জানান ভাই,0,politics
হুম,0,politics
ধন্যবাদ রবিন আপুকে,0,politics
বি এন পি কেনো অতিথ ভুলে যায় কি নির্বাচন করে তিনি প্রধানমন্ত্রী হয়েছেন সালে কি ভোটার লিস্ট করেছে এককোটি চল্লিশ হাজার ভুয়া ভোটার কে এন হাসান কে উপদেষ্টা করতে গিয়ে কি করেছেন এযাজউদিদনকে রাষ্ট্রপতি করে কতো নাটক করেছেন।,0,politics
এখন কে কার সমতুল্য তা নিয়ে তর্ক না করে একটা উদাহরণ দেয়া যাক কেউ যদি আপনাকে একটা পরীক্ষায় ফেলে যে আপনার মাথায় পিস্তল ধরে বলে যে এই দুইটা পাত্রে কিছু পানি রাখা আছে আপনি এখান থেকে আপনার ইচ্ছা মত একটা পাত্রের পানি পান করুন তাহলে সে আপনাকে মুক্ত করে দেবে তখন আপনাকে বলা হলো একটা পাত্রে রাখা আছে বিষ মেশানো কিছু পানি আরেকটা পাত্রে রাখা আছে মানুষের প্রস্রাব তখন আপনি কি করবেন অবশ্যই বাঁচার জন্য অশ্রাব্য কই পান করবেন তারপর তার কাছ থেকে মুক্তি পেতে চাইবেন তো কি বুঝলাম না এখন বলা যায় খালেদা জিয়া যখন দেশের প্রধানমন্ত্রী হয়েছিল তখন দেশে ছিল ক্রান্তিকাল অভাব যোগ্য নেতৃত্ব দেওয়ার মতো নেতার অভাব আর শহীদ জিয়াউর রহমানের বর্তমানে বেগম জিয়াই ছিল একমাত্র যোগ্য কিন্তু নেতা হবার মতো কোনো যোগ্যতা ছিল না তিনি ছিলেন বিখ্যাত রাজনীতির কোন মেধা তার ভিতরে ছিল না আর তাই সে অন্ধের মত প্রধানমন্ত্রী হয়ে গেল অন্যদিকে ওবায়দুল কাদের নিজেই নিজের যোগ্যতায় রাজনীতির শিক্ষায় আজকের জায়গায় অবস্থান করতেছে তার অবস্থান এতটাই উপরে যে প্রধান মন্ত্রীর পরেই সে নেতৃত্ব দিচ্ছে তাহলে তার অবস্থান কোন দিক থেকে ছোট প্রধানমন্ত্রী আর ওবায়দুল কাদের,0,politics
ওনার কারনে এবং ওনার সাথে সেলপি তুলে ফেসবুকে বায়রাল করে কত গুলো সাধারন ও অসহায় মানুষকে হাতে না মেরে বাতে মেরে জেলে পাঠিয়ে তাদের উপর একের পর এক পরিকল্পিত ভাবে অমানবিক নির্যাতন শুরু করে তাদের আথিক টাকা পয়সা সয় সম্পদ বিকরি করায় সব লুটে নেন।এবং আজ অত্যান্ত দুঃখের সাথে বলতে বাদ্য হলাম আর গোপন করে রাখতে পারছিনা?মহিপাল ছিলো বিএনপির গাটি আমি যখন এই গটনা গুলো দেখছি এবং জানতে পারলাম তখন থেকে আর এখন আমি মহিপালের সেই মানুষ টির কথা বলছি।সবাই জানে সে কতটা বয়াবহ রুপ।তার উপরে দৃশ্য টা রুপ।কিনতু বিতরটা হলো টাকা আর টাকা। সে একজন বিজা বিডাল তার নাম স্বপন মিয়াজী।বতমানে মহিপাল নং ওয়ার্ডে কাউনসিলর এবং প্যানেল মেয়র টু।তিনি কিলিন ইমেজে চলাপেরা করেন। ফেনীর মহিপালের সহজ সরল অতী সাদারন দানশীল ব্যাক্তি এবং শিল্পপতি যাদের ত্যাগ আর অসীম সাহসীকতায় মহিপাল আওমীলিগ পরিপুর্ন সফল হয়।এবং তাদের অনেক অত্যাচার সইতে হয়েছে।তখন আসলো থেকে বিএনপির বিপি জয়নাল ক্ষমতায়।তখন এক বাসের ডাইবার শমিক সদস্য হন তার মিলন।ওরপে হাডু মিলন এই কুওার বাচ্চা কতগুলো পরিবারকে পথের বিখারি করেছেন কতগুলো মানুষকে গাডী চাপা দিয়ে মেরেছেন কত গুলো আওমীলিগ কর্মি দের পায়ের রগ কেটে দিয়েছেন মেরে পেলেছেন তখন থেকে সে কোটি কোটি টাকা হাতিয়ে নিয়েছেন।ঠিক তখন এ বিপএনপির শেষ পযার্য় দেখছেন বিএনপি আসবে ঠিক তখন এই মিলন স্বপন মিয়াজী চিলো একজন ফুল ব্যাবসায়ী।এই মিলন তার অপকর্ম ডাকতে এবং আওমীলিগের ত্যাগি নেতাদের ভিবিন্ন ভাবে গুজব রটিয়ে এবং তাদের পরীবারের উপর একের পর এক অত্যাচার একের পর এক ত্যাগি নেতার ছেলেদের নেশায় পরিনত করে মামলা ডুকিয়ে দমন করতেন।এসব মুল বুদ্দি দাতা এই বিএনপির নেতা মিলন।এই হাডু মিলন স্বপন মিয়াজিকে আওমীলিগে ডুকিয়ে তাকে রাজনিতি টিকে থাকার অর্থের যোগান কিনতু কেউ জানতো না।পরে দিরে সব কিছু প্রকাশ পায়। বতমানে এখনো সে কোটি কোটি টাকা কামিয়ে জাচ্চেন।এখন সেই মিলনকে স্বপন মিয়াজী আওমীলিগে ডুকান।আওমীলিগে আপস করে তাকে রাজনিতি পরিনত করেন।এবং প্রকৃত প্রবিন আওমীলিগের পতি তাদের এবং তাদের সহযোগীদের বিএনপির জালাও পোরাও হামলা মামলায় ডুকিয়ে দিলেন তাদের সর্ব শান্ত করে দিলেন।একের পর অত্যাচার এখন আরো দুটি বংশকে নিরবংশ পথে নিয়ে যাচ্চেন।প্লিজ প্রিয় মিডিয়া ভাইয়েরা আপনারা আমার বক্তব্য নিউজ করুন এবং এই তথ্য ইকবাল সোবান চৌধরী এবং মাননীয় প্রধান মন্ত্রির কাছে তথ্য জানানোর জন্য আকুল আবেদন করছি।আল্লাহ মালিক,0,politics
এটা বেপার না বাংলাদেশে,0,politics
খালেদা জিয়া প্রধানমন্ত্রী ছিলেন এবং উনি অবশ্যই সৎ ছিলেন ওবায়দুল কাদের উনিতো এখন ক্ষমতা পাওয়ায় তাকে জনগণ চিনে,0,politics
কাদের একটা ঘড়ি বিক্রি করতে পারলে আমি বড়লোক হতে পারতাম🤔🤔🤔 😋😋আপসোস😋😋,0,politics
এরা আমাদের শরীরের রক্ত ঝরার ট্যাক্সের টাকা নিয়ে দামি দামি ঘড়ি পড়ে এদের একদিন বিচার হবে আল্লাহর দুনিয়ায়,0,politics
সবাই লিগ,0,politics
আপনাকে ভালবাসি ভাই ভয় হয় আপনার জন্য সাবধানে থাইকেন সাহসীদের তো ঠাই এ দেশে দুস্কর হয়ে গেছে,0,politics
কথাই রাজধানি আর কথাই ছোদ মারানি মেনটেল আওমিলিগ,0,politics
যিনি মন্ত্রী থাকবেন তাকে যেন দলের সাধারণ সম্পাদক পদ দেওয়া না হয়।,0,politics
কা কা কা তুমি পতিতার মাসিকের পেন্টি ধোওয়ার কাজ করতে পারো???,0,politics
দেশ আজ কোথায় যাচ্ছে সঠিক বিচার না হওয়ার দরুণ আজ এ অবস্থা,0,politics
হায় রে বাংলাদেশ কোথায় আজ আছি আমরা এই আওমিলিগ একটা সন্তাস দল তারা আমাদের মা বোন এবং ইজ্জত দেশের সম্পদ নংরা পরিবেশ তৈরি করতে ছে আল্লাহর গজব পড়বে,0,politics
আওয়ামিলীগ সন্তারাসেরাই দেশটি শেসে করেছ হাসিনাকে মারতে হবে তারপর দেশ টিক হবে,0,politics
ইনু মাথা গরম হলে কিন্তু তোকে মারবো ও কাদের কে ও বেশি মারবো গুলামের বাচ্চারা দোনো জন গাঁদা,0,politics
এ টাকায় ত অনেক বেকার ব্যাবসা করে সাফল্য পেতে পারে তবে তিনি একজন মন্তী তারহাতে মানায়,0,politics
পেট নীতির জন্য নতুন কেও,0,politics
ওবায়দুল কাদের ও আউট হবে আওয়ামী লীগের সাধারণ সম্পাদক থেকে নিশ্চিত,0,politics
বাংলাদেশের আরেক নাম কচুজিয়া,0,politics
সাংবাদিক ইলিয়াস আপনাকে মানে ইসকন আলম উপাধি দিছে সেটা নিয়ে আপনার মতামত চাই এই কথা নির্বাচন এর আগে করলে ভালো হতো চৈত্র মাসে ইসকন আলম শীতের রসের কথা বলছে,0,politics
বেগম খালেদা জিয়া বাংলাদেশ,0,politics
কোথায় সোভিয়েত ইউনিয়ন আর কোথায় বিনোদন পুর ইউনিয়ন। হা হা হা হাস্যকর। খালেদা জিয়া সাথে ওবায়েদুল কাদের তুলনা করা প্রশ্নকারী একটা গোবেট।,0,politics
নোয়াখালীর টাকায় এগুলোর দাম টাকা। বাংলাদেশের টাকায় হিসাব করলে তো হবে না।,0,politics
এই টাকা গুলি কাদেরের বাপের টাকায় কেনা,0,politics
টয়লেট টিস্যু ব্যবহার করে পকেটে রেখে দেওয়া যেমন বুদ্ধিমানের কাজ নয়! তেমনই জয়ের মালা পরিধান করেও আত্মতৃপ্তি না হওয়া লোকগুলো বুদ্ধিমান নয়!,0,politics
কাউয়া আর হাউয়া লগে দেশনেত্রী বেগম জিয়ার তুলনা এটা হাস্যইকর😆😄😃,0,politics
এসব করে আর কী হবে ভোট চুরি করে ক্ষমতায় জাইয়া এখন যতই পরিবর্তন করেন না কেনো কোনো লাভ নেই আওয়ামী লীগ দলটাই একটা ভাইরাস বাঙ্গালী জাতির জন্য,0,politics
আচ্চা একটা প্রশ্ন দেশে কি একজনই বংগবন্দু ছিলেন যার হত্যার বিচার করতেই হবে আর কেউ মরেনি??? আর একজনের বাবা মরেছে আর প্রতিদিন যে হাজার হাজার কারও না কারও স্বজন বাবা মা ভাই বোন স্বামী মরছে কই তাদের কথা বা বিচার তো কেউ করে না???,0,politics
মরা’ নামে এক ভবঘুরেকে ধরে এনে ধর্ষক হিসেবে সংবাদমাধ্যম ও কোর্টের সামনে হাজির করে।,0,politics
স্বভাপতি সবসময় ফিক্সড থাকবে।।।,0,politics
আপুর কথা রাইট,0,politics
ভাই খুব নিয়ে ভিডিও দিলেন।। ভাই আল্লাহ আপনাকে আল্লাহ নেক হায়াত দান করুক।❤,0,politics
ধন্যবাদ রুমিন ফারহানা আপা কাদের একটা তুমা ফু দিলেই নাই,0,politics
ভাল মানষ কোন দিন গালা গালী করে না ভদ্র মানুষ কোন দিন গালা গালী করে না,0,politics
আওয়ামী লীগ মানেই বিনোদন।,0,politics
উপু উকিল তুই যে ভোট চোরি করে ক্ষমতায় আইছত মাগি নিজের চিন্তা কর ক্ষমতা হারালে তোর যে কি হবে।।,0,politics
ভাই দারি তে আপনাকে অনেক সুন্দর লাগছে মাসা আল্লাহ,0,politics
বাঁশ !!!,0,politics
ভোটের আগে কাজ দ্যখাচেছ দেখুন,0,politics
ইমুকে বাদ দেন ভাই,0,politics
😀😁😁😂 বাটপার নুরু কে মার,0,politics
ইনু ও ওবায়দুল এরা মন্রী হিসাবে অজগ্য,0,politics
হায়র‌ে আমার বাংলাদ‌েশ ! শ‌েখ মুজিব ক‌েমন এক ম‌েয়ে র‌েখে গ‌েলো য‌ে ক‌িনা কুত্তা লীগ‌ের মা ! এই কুত্তা লীগ গুল‌োক‌ে গাল‌ি দ‌িলেও কুকুর‌েরা লজ্জায় মারা যাব‌ে । য‌েসব ছ‌েলেরা কুত্তা লীগ কর‌ে তাদ‌ের বাপ মাও কুকুর । কারন তারা তাদ‌ের কুকুরগুল‌ো সুশ‌িক্ষা না দ‌িয়ে রাস্তায় ছ‌েড়‌ে দ‌িয়েছে,0,politics
জবাবদিহি না তাকার কারনে অাজ এ ই সমস্যা,0,politics
খমতাই কেও সারাজীবন টিকে থাকতে পারে নাই আর পারবেও না কুত্তালীগতো শিবিরকেও হার মানাইছে! একবার শুধু খমতাটা যাক তদের কাছ থেকে আশা করি তদের কোনো অস্তিত্ত থাকবে না!,0,politics
ইনু তোমার সময় কাছে কাছে আসছে হাসিনা বুঝতে পারছে তুমি জে একটি রাজাকার তোমাকে সেখহাসিনা বাবের পতিসোদ নেবেন ফাঁস দিবে,0,politics
আসলে কি দেখেন জখন কন প্রবাসী চাকরি করে মাসে বেতন লাক টাকা পায় সে আবার কিন্তু ওভার কাজ করে বেস্তি কিছু টাকা কামাতে পারে তাহলে আমাদের কাদের সার কি কোটি টাকা দামের ঘড়ি পরতে পারে না বেতন লাখ টাকা হলে তিনি ও ত আমাদের দেশের জন্য অনেক ওভার কাজ করেন,0,politics
তুমি সত্তিকারের একজন দেশপ্রেমিক এই দেশ দেশের মানুষ আছে তোমার সাথে ইনশাআল্লাহ,0,politics
আওয়ামীলীগ নেত্রী তো জানেন না যে এ নয় এ এসেছিলো,0,politics
অতি লোভ করিলে আদশর্ নষ্ট হয়। আদশর্ হীন ব্যকতিদের আবস্থা আরো খারাপ হয়। লীগ চেয়ছে নুরকে নূর যদি না থাকে তাদের আদশের্,0,politics
তাহলে অনেকদিন পর একটা জিনিস বুঝতে পারলাম অনুপ্রবেশকারী ভিতরে ওবায়দুল কাদের অন্তর্ভুক্ত হলেন আহা কি শান্তি,0,politics
কি কয় অপু টপু এরা দামড়া গরুর মত এক দিকে টানে এরা নেয় অনন্যয় কিচু বুজেনা কেন এদেরকে টক শোতে আনা হয়,0,politics
আওয়ামীলিগের চোর সম্পাদক ওবায়দুল কাদের। এগুলি বাংলাদেশের শেখাসীনা ডাকাত পোষতেছে। দেশের সম্পদ লুট করে বিদেশে বড়ো বড়ো বিলডিং নির্মান জন্য বসে আছে।,0,politics
সাহেদ আলম একটা দালাল,0,politics
ঘরির দামের বিপরিতে পিয়াজ কিনে দেয়া হোক,0,politics
প্রশাসন এর এত খারাপ অবস্থা,0,politics
কি কয়তাছে হে?,0,politics
কত কথা কত লেখা দেখলাম,0,politics
রেহানা বুবুর কপাল আর খুললো না😃😃,0,politics
আলুর দোষ ঢাকতে! 🤣🤣🤣,0,politics
রূমিন আপা রাইট,0,politics
ভাংগা সুটকেস আর ছেরা পেন্ট এই দুইটা শব্দ হলো মেডাম অপু উকিলের ব্রম্মাস্র যেটা তিনি প্রত্যেকটা টকশোতে বলে যান।,0,politics
তুই ইনু বাংলাদেশের কোন আসনে একজন মেম্বর নির্বাচিত হতে পারবি না।,0,politics
ভালো হতে পয়সা লাগে না। আর এখানে দালাল মার্কা নায়ক নায়িকা আছে,0,politics
বি এন পি যারা করে তারা পাগল বি এন পি কোন দল বাংলাদেশে ছিলো না থাকবে না,0,politics
ঐ গোলি সব চোরের গোষটি সব,0,politics
কাদেরের হাতে হারিকেন ধরায় দিয়ে নোয়াখালীতে পাঠানো হোক।।।,0,politics
ওপু উকিল না কি যেন নাম মহিলার এ তো পুরাই মাতারি!খালেদা জিয়া ভোট চুরি করলে শেখ হাসিনা ত মানুষকে ভোট দিতেই দেয় নাই!ভোটকেন্দ্রে প্রিজাইডিং অফিসারেরা নিজের হাতে নৌকায় সিল দিসে আর বাক্সে পুরসে।আজাইরা যতসব মূর্খের প্রলাপ!,0,politics
হইয়া গেলা বিম্পি দলিয় 😂 এই মনে কর যে ভাই দাড়ি আরেকটু বড় হইলে শিবিরের তকমাও আসবে 🙂🙂 শেষের কাভার নেওয়াটাও ভলো হইছে নইলে চ্যানেল টাও যাইতো 😅😅,0,politics
ভাই আপনি একটা জিনিস জুতার বাড়িও দিলেন আবার সালামও দিলেন।😎😎😎,0,politics
আকাশে চাঁদ উঠলে সবাই দেখবে,0,politics
সরকার দৃষ্টি আকর্ষন করছি নুরকে সিকিউরিটি দেবার দরকার,0,politics
ওরা মানুষ না ওরা অ।।।।।।।।।।।।।।।।।।।।।।।।।।।।।।।।।।।।,0,politics
খালেদা এতিমের টাকা চুরি করে খাইছে এটাও একটা নাম এইকথা বুলেজাস কেন,0,politics
কাদের কে বাদ দিলেই চলবে,0,politics
ভাই চালিয়ে জান আমরা আপনার পাশে আছি,0,politics
আমার হাতের ঘড়ি এটা জামায়াতের চক্রান্ত,0,politics
অসাধারণ ভাই,0,politics
ওবায়েদুল কাদের আর খালেদার তুলনা হয়না তা সত্যি কেননা কাদের রাজনীতি করে নেতা হয়েছেন আর খালেদা সেনা শাসকের অবৈধ একটি প্লাটফর্ম থেকে।,0,politics
এই ঐক্যটাকে বুহুদিন ধরে রাখতে হবে।,0,politics
ভাই ভিডিও দেখার আগেই লইক। তবে ভাই আপনার কি রাজনিতিতে যুগ দেওয়ার সম্বাবনা আছে?,0,politics
এরা কারা😂😂😂😂,0,politics
আজকে দেশে এত ঝামেলার জন্য একমাত্র দায়ী কলঙ্খীত নারীরা,0,politics
খালেদা আমার ও বাংলাদেশের লাচাও,0,politics
তুলনামুলক ভাবে কাদের স্যার যোগ্যতা রাখে লিডারশীপের।,0,politics
আয় ভাই হাতে হাত মিলাই🤝🤝🤝❤,0,politics
আপনারা ঐক্যবদ্ধ হোন,0,politics
একটা ও লীগের দিকে নাই ছী লীগ ছী আপনাদের লজ্জা নাই।,0,politics
জানোয়ার ইবলিশ সয়তান গুলা এক জাগায় হয়েছে সয়তান মিলে সয়তানের সাথে,0,politics
সারা বাংলাদেশের ছাএ সমাজ এক হও কেনো ভিপি নুরুল হকের উপর এতো হামলা? আমরা জানতে চাই।,0,politics
মন্ত্রী বানায় দে মা লুটেপুটে খায়,0,politics
এদের গলার স্বর এত উপরে উটছে যে বাবারে বাবা,0,politics
মাননীয় নেত্রীকে ধন্যবাদ ইনু কে পিনু করায়,0,politics
তৈল যতই মর্দন করা হোক ৷ পিছল ছাড়া হস্তগতো আর হবেনা ৷,0,politics
আমার খুব হাসি পাচ্ছে,0,politics
আওয়ামিলীগ কে পছন্দ করলেও এই শালাকে একটুও ভালো লাগে না।,0,politics
আপনাদের ভিডিওটি অনেক ভালো লাগলো ধন্যবাদ,0,politics
কথা গুলো খুব ভাল লাগছে,0,politics
তারিকের টা।বাদ।দে।খাননি।এখন।তোরা।চুরি। করছ।কি।জন্য।তোরা।তা।তো।ভালো।,0,politics
শেক হাছিনার পদতেক চাই,0,politics
তোমারে মহাজোটে লাগবেনা,0,politics
যাঁরা দেশ প্রেমিক। তারা তাদের দায়িত্ব পালনে অটল থাকে,0,politics
আমার চ্যানেল সাবস্ক্রাইব করতে লোগোতে ক্লিক করুন আমিও আপনার চ্যানেল সাবস্ক্রাইব করব। কমেন্ট করে জানাবেন।,0,politics
শোভন রাব্বানী রে খায়া দিছে এই শালা,0,politics
ভাই আপনার উপস্থাপনা এক কথায় অসাধারণ। আমি একটুও না টেনে পুরো সেশ করছি,0,politics
ডুগডুগি বাজাও,0,politics
আমিতো মনে করতাম ওবায়দুল কাদের ভালো লোক এখনতো দেখি বড় চোর।এদের বিচার আললাহ এক দিন করবে।,0,politics
সাধারণ মানুষ হয়ে বলব।কোথায় আসনে নির্বাচিত হয়ে প্রধানমন্ত্রী আর কোথায় ওবায়দুল কাদের সাহেব।,0,politics
হা হা হা বিনোদন,0,politics
আওয়ামীলীগ এখন দেশ চেরে জাওয়ার চিন্তা করছে😁😁😁😆😆😆😆,0,politics
ইনু মিনু টিনু ভাই হাসু আপু হিসু করে দিলে তোমারা খেয়ে ফেলো তাহলে ঐক্য টা আরো কিছু দিন টিকে থাকতে পারে। আর না হয় তোদের পিটের চামড়া থাকবে না।,0,politics
ভোট কারচুপি কারা করে তা জনগণ স্বচক্ষেই দেখেছে । কথা অাছেনা চোরের মায়ের বড় গলা,0,politics
আপনাকে কিছু না বলে শুধু ডিজলাইক দিলাম বেয়াদপ কোথাকার,0,politics
সাবাস রুমিন ফারহানা,0,politics
কাঊয়ার গলা শূকিয়ে আসছে,0,politics
আমাদের গর্ব আমাদের রাজনীতিবিদেরা। এমন মোটা চামড়ার মানুষদের পেয়ে আমরা কি গর্ব না করে পারি ভোট চোর ভোট ডাকাত পাগল মাতাল আরো কত কি। তারা অসুস্থ হলে মানুষ তাদের মৃত্যু কামনা করে এরপরেও দেখুন এদের সামান্যতম লজ্জা নেই। এমন রাজনীতিবিদদের পৃথিবীর আর কোথায় পাবেন,0,politics
বাবা তুমি এগিয়ে যাও তোমার মত সোনার ছেলে দরকার,0,politics
কুয়েতে আমি দিনার দিয়ে কিনিছি।বাংলার,0,politics
এই হলো হারা মি দেশ।,0,politics
কাওয়ারে লুচ্চাকে সত্ বলায় না হেসে পারলাম না হা হা হা ।,0,politics
আল্লাহ এই জন্যই তাকে উঠিয়ে নিতে চেয়েছিলো,0,politics
জয় বাংলা,0,politics
ইনু মেনন মোতিয়া সহসাই আস্তাকুঁড়ের জঞ্জালে পরিনত হতে যাচ্ছে। এখন শুধুমাত্র সময়ের ব্যপার। যেহেতু তাদের দ্বারা আওয়ামী লীগের কার্যসিদ্ধি হয়ে গেছে।,0,politics
কলেজের মধ্যে বাল্যশিক্ষা আমাদের মধ্যে কিছু নেতা খেতা আছে অনেক খারাপ শিক্ষার দে,0,politics
সৈয়দ আশরাফের জুতার সমান হয়নি ওবায়দুল কাদের সৈয়দ আশরাফ আওয়ামিলীগ এর কান্ডারী চিলেন টাকার নয়৷ ওবায়দুল কাদের মুখে বড় কথা বলে ভিতরে চুর,0,politics
কাউকা কাদের,0,politics
ফাডা কষ্ট,0,politics
গনতন্ত্র আজ গদি তন্ত্র ।।।,0,politics
আওয়ামী লীগ আর কুত্তালীগ সব কিছুই দখল করে নিছে,0,politics
দেশটা দিন দিন অধপতনের যাচ্ছে। এই সব কুত্তা লিগের বিচার করবা কে?,0,politics
কাউয়ার সাথে হিরো আলমের তুলনা চলে।,0,politics
ওবাইদুল কাদের সে একজন হাজারো নারীর এক খদ্দর,0,politics
বি এন পি এগিয়ে যাও ।,0,politics
ভাল্লাগছে ভাইয়া 😄😄😄,0,politics
মিথ্যাবাদী ফালতু ইউটিউবার,0,politics
ঠিক বলেছেন,0,politics
বেগম জিয়ার জুতার যে সন্মান আছে তাও কাওয়া কাদের নাই,0,politics
কোথায় খালেদা জিয়া? আর কোথায় কাউয়া হাম বা বে টী কয় কি? বুজে আসেনা,0,politics
ঘুরে ফিরে একই মুখ গুলা এরা কি লেখাপড়া কর‍তে গেছে নাকি এইসব রাজনীতি করতে??? আর এই একই কথা সাংবাদিকদের সামনে জাতি তাদের নাটক দেখতে দেখতে ক্লান্ত।,0,politics
ছাএ লীগ আর প্রশাসন এরা তো ভাই ভাই,0,politics
যুক্তি গুলো ঠিক আছে তবে আমার কিঞ্চিৎ মনে হয় তার ঘড়ি গুলো উপহার হিসেবে ও পেতে পারেন কেউ ভূল ভাবে নিবেন না সবাই এটা দেখবেন তাদের প্রশ্ন করলে আমার জবাবটাই দিবেন,0,politics
কাদের খালেদা জিয়ার জুতার সমান না।,0,politics
একজন শিক্ষকের সন্তান আজ হাজার হাজার কোটি টাকার মালিক হাতে যদি কোটি টাকার ঘড়ি পরে এতো টাকা কয় হয়।,0,politics
ভিপি নুর ভাল লোক,0,politics
কা কা কা করিয়েন না।,0,politics
গুলিস্তান থেকে কিনছে,0,politics
আল্লাহ না করুক ভারতীয় কোনো প্রভাব না থাকলেই হয় ইসকন,0,politics
একটা কামের কাম করছে শেখ হাসিনা হালা কাউয়া কাদের হেতে ক লেখতে কলম বাংগি ফেলে হেতারে দিছে সাধারণ সম্পাদক,0,politics
সমালোচনা ভালা দিক কিন্তু সেটা সবার বেলায় হওয়া উচিত। যদি সেটা না হয় তবে নিরপক্ষ হয় না।,0,politics
ভাই আপনার মুছ কাটেন না কেন?,0,politics
এই অপু উকিলরা আর কত একই ভাংগা রেকর্ড বার বার বাজাবে? অপু উকিল একজন চরম অভদ্র মহিলা। ভোট চুরির কথা আওয়ামিলীগের মানায় না।,0,politics
অপুর কোন কথা হয়না,0,politics
সাহসী ভিডিও!!!,0,politics
দেখেন ইনু সাহেবের পল্টি মারা ! মরহুম শেখ সাহেবের মৃত্যুর পর টেঙ্ক এর উপর নেচেছিল এই জঙ্গী ইনু । স্বাধীনতার পর গনবাহীনির নেতা ছিল এই জঙ্গী ইনু ।,0,politics
উকিল ত দালাল জাতি।,0,politics
হায়রে দেশ,0,politics
আওয়ামী লীগের প্রার্থী বেশি মেকআপ এর কারণে হিজলার মত দেখতে,0,politics
তুই তো কা কা কা,0,politics
বি এন পি আগে বছর কমতায় ছিল দেশের জন্য কি করেছে। বি এন পি আর লাগবে না।,0,politics
এতো সাহস ভাই আপনার!!!,0,politics
ভাই প্রথম ভিডিওতেই ভক্ত হয়ে গেলাম!♥,0,politics
যাদের পেট ভরছে তারা এখন কিছুদিন অবসরে যান আরো যারা আছে খালি পেটে তাদের এখন পেট ভরার সময়,0,politics
আ লীগ মিথ্যাবাদী,0,politics
এ সবে মানুষের ভোগান্তি আরও বারতেছে,0,politics
বাংলা দেশে সারকার এখন চুর ডাকাত সন্তাসি দের সরকার। ধষর্কের সরকার। আমি একটা কথা বলতে চাই যে দেশে দিনের বেলাই মেয়ে স্রামি সশুর সাশুরি সামনে ধর্ষন করা হয় বাংলার এক বোনকে সেদেশে গন্রত্রান্তিক দেশ বলা যায় না? সরকার অপরাদিদের বিচার করছেনা কারন তাহলে তারা খমতাই থাকতে পাবেনা।,0,politics
আমাগো ছাত্র লীগের চামচার লগে খালেদা জিয়ার তুলনা হয় না😴,0,politics
আল্লাহ অবশ্যই এসব অন্যায়ের শাস্তি দিবেন শাস্তি এদের পেতেই হবে আজ হোক বা কাল,0,politics
তোর কারনে রাস্তায় প্রচন্ড জ্যাম লেগে আছে।,0,politics
ছোট আপা কি জিবনে কোনদিন মসনদে বসবে না?,0,politics
বড় বড় বাস নিয়ে আ লীগকে পিঠাও,0,politics
আওয়ামী,0,politics
ভাই খুব রিস্ক নিয়ে নিলেন ভাই❤ দোয়া করি আপনার কিছু না হোক।,0,politics
ও তো হিজরা,0,politics
এদের পরিণতি এরকমই হয়। এ তো মনের দিক থেকে আওয়ামী নয়। সুবিধাবাদী। একা নির্বাচন করলে বুঝতে পারতো।,0,politics
আপনাকে এই জন্যই এতো ভালো লাগে ভাই সদা সত্যের পথে থাকবেন ইনশাআল্লাহ আল্লাহ আপনার মঙ্গল করবেন।💜💜💜,0,politics
শেখ মুজিব পারেনাই বাকশাল চালু করতে।তাই এখন আওয়ামী লীগ সরকার সেই বাকশাল চালু করে দিলো। বাহ্ আগামী প্রজন্ম কি শিখবে? বর্তমানই হবে ভবিষতের অতীত। আগামী প্রজন্ম অতীত জেনে শুধু ধীতকার জানাবে। এখনো সময় আছে বাংলার মানুষের নিজ নিজ স্বাধীনতা দিন। নয়তো ক্ষমতার হৃদবদল হলে আপনাদের অবস্থা কোথায় দাড়াবে সেটা ভাবুন।,0,politics
অাওয়ামিলিগ অামাদের দেশকে লুটে নিচ্ছে,0,politics
মজা পাইলাম বাই,0,politics
শান্ত ভাই তোমাকে অনেক ভালবাসি,0,politics
আওয়ামী লীগ হলে সব সম্ভব,0,politics
ওবায়দুল কাদের এমন একজন রাজনীতিবিদ যে কাজের চেয়ে কথা বেশি বলেন।,0,politics
কাদের চাচা ত পাগল ওকে মন্ত্রিত দিল কে রে,0,politics
আসলেই চোরের মায়ের বড় গলা,0,politics
ছাগলের সাতে বাঘের তুলনা 😂,0,politics
খালেদা জিয়া এতিমের টাকা মেরেছেন তাই তার সাতে ওবায়দুল কাদের সাবের তুলনা হয় না,0,politics
পরের টা কথা শুনলে মনে হয় এটা পাগল মানুষ বঝে,0,politics
কাদের কে এক কথায় বলে কাউয়া কাদের আর জনগণের মা বলা হয় বেগম জিয়া ।,0,politics
ভাই তোমার সাহস দেখে আমি অবাক হই!! আমার লাইফের দেখা সেরা সত্যবাদি ইউটিউবার তুমি ভালোবাসা নিও!,0,politics
জনাবা বেগম খালেদা জিয়া আমাদের দেশের মা।। আর কাউয়া তো গু। খায়।।।,0,politics
জিয়াউর রহমান সাহেব যখন মারা যায় ।তখন তার ভাঙা সুতকেস ছিল । তাহলে কয়টা আলাদিনের প্রদীপ পাইলে এই কয় দিনে এত কোটি টাকার মালিক হয় জিয়া পরি বার । আপনার ডকুমেন্টারি টোটালি ফালতু ।,0,politics
সময় আসতেছে তরে ধরার,0,politics
এগুলো নিয়ে কেয়ামতের দিন উঠবে,0,politics
ভাই ফাটিয়ে দিয়েছেন।,0,politics
হা,0,politics
চি চি,0,politics
আমরা প্রোবাসি হাসিনারে টাকা দিয় সেই টাকাই দেশ চলে তাই আমরা প্রোবাসি বলছি নুরু ভাইয়ের যদি কিছু হয় দেশে আর কুত্তা লীগ থাকবেনা আগুন জলবে সারাদেশে,0,politics
এই তো দেখি চটির গল্পের থেকে ও সেক্সি,0,politics
সব চোর শেখ হাসিনা বলেন খালেদা বলেন তারেক জিয়া বলেন সব চোর উবাইদুল কাদের বলেন জয় বলেন এরা কেনো খমতা নিয়ে এতো লাফালাফি করে শুধু লুটপার করে খাওয়ার জন‍্য। দেশের কথা ভাবার মতো মানুষ নাই লক্ষ মানুষের মধ‍্যে একটা পাওয়া মুসকিল এবং যারা আমলীগ বিএনপি নিয়ে লাফালাফি করে সবাই নিজেদের সারথ্যর জন্য লাফালাফি করে দল খমতাই গেলে টেন্ডার বাজি ও খমতার অপব‍্যবহার করার জন্য এই মানুষ গুলির ভিতর কোন দেশ প্রেমের কোন নমূনা থাকেনা শুধু মুখেল বুলি।।,0,politics
ত্রুইওএর‍্য,0,politics
খালেদা জিয়া বাংলাদেশ না বাংলাদেশের সাথে খালেদা জিয়ার তুলনা এটা কুলাঙ্গার ছাড়া আর কেউ করতে পারে না হ্যাঁ খালেদা জিয়া সেই নেত্রী যার জন্মের ঠিক নাই জন্ম তারিখ কয়েকটি হ্যাঁ খালেদা জিয়া সেই নেত্রী যিনি পৃথিবীর ইতিহাসে একমাত্র অষ্টম শ্রেণী পাশ যার কোনো সার্টিফিকেট নাই হ্যাঁ খালেদা জিয়া সেই নেত্রী যিনি মুক্তিযুদ্ধের সময় পাকিস্তানি সেনাদের সেবা যত্নে লিপ্ত ছিলেন হ্যাঁ খালেদা জিয়া সেই নেত্রী বাংলাদেশের টি জেলায় বোমা হামলায় নেতৃত্ব দিয়েছেন হ্যাঁ খালেদা জিয়া সেই নেত্রী যে কি না আগস্টের গ্রেনেড হামলার নেতৃত্ব দিয়েছেন হ্যাঁ খালেদা জিয়া সেই নেত্রী যার শাসনামলে বাংলাদেশ দূর্নীতিতে বার টানা বিশ্ব চ্যাম্পিয়ন করিয়েছেন হ্যাঁ খালেদা জিয়া সেই নেত্রী যিনি বাংলাদেশকে একটি সন্ত্রাসী দূর্নীতি বাজ ও ভয়ংকর রাষ্ট্রে পরিণত করতে চেয়েছিলেন হ্যাঁ খালেদা জিয়া সেই নেত্রী যিনি এতীমের টাকা চুরির দায়ে জেল খাটছেন হ্যাঁ খালেদা জিয়া সেই নেত্রী যিনি তারেকের মতো অশিক্ষিত কুলাঙ্গার দূর্নীতির সূর্য সন্তান কে জন্ম দিয়ে বুড়া বয়সে জেল খাটছেন আর কিছু বলবো ???????,0,politics
বেগম জিয়ার সাথে ওবায়দুল কাদেরের তুলনার প্রশ্ন আসে কোন সাহসে?হাস্যকর।,0,politics
উনি নরম মনের মানুষ তাই কাউকে না বলতে পারেন না। বাশ দিলেও হা হা হা,0,politics
বিশ্ব এবং বাংলাদেশের কোন মিডিয়ায় এ ধরনের খবর দেখলাম না এটা তোর বানানো খবর,0,politics
জে মার খায় সে নেতা হয় মনে রাখবে ভাই,0,politics
ভালবাসার প্রিয় ভাই❤ আশাকরি সবসময় এই রকম সত্যের পথে থেকে সত্যি কথা বলে যাবেন।,0,politics
রোস্টতো সবাই করে এমন দুঃসাহসিক রোস্ট করার সাহস একমাত্র এই লোকটার ই আছে সেলুট বস♥♥♥।,0,politics
তোকে এক দিন পিটবো আমার ইচ্ছা,0,politics
মিত্য বলায় আগমী লীগের অভ্যাস,0,politics
আমি পটেটু চিপস খাচ্ছিলাম। হঠাৎ আঙ্গুলে কামড় খেলাম তারপর বুঝতে পারলাম গণতন্ত্রের হালধরছে কেউ।,0,politics
বীর মুক্তিযোদ্ধা কাদের স্যার,0,politics
গনতন্ত্র মানে জনগণের শাসন জনগণ জাকে ভোট দিবে সে ক্ষমতায় যাবে আপনাদের কে তো জনগণ ভোট দেয়নাই আপনারা কিভাবে ক্ষমতায় আছেন বাংলাদেশের ষোল কোটি মানুষ জানতে চাই । ভোটার বিহীন সরকার বাংলাদেশে নাই দরকার ।,0,politics
কতো বড় মিথ্যা বাদি কথায় কথায় দরা খায় তার পরো খমতার কারনে বরাই করে,0,politics
অবাইদুল কাদের একটা ছুর,0,politics
আমার ঘড়ি এইটা দাম কত? যেখানে হাজার কোটি টাকা কিছু টাকা কোটি টাকার ঘড়ি কিছু না ভাই,0,politics
বেগম জিয়া বর,0,politics
অপুর সাথের মেয়েটা সেক্সি তাকে বলে দিও,0,politics
কাদের তো আওয়ামী লীগের অনেক দিন দালালী করলো ?? 🤔🤔,0,politics
খালেদা নর্দমায় পতিত হয়েছে চাপা মেরে লাভ নাই।,0,politics
কবরে কি ভাবে সময় দেখবা ?,0,politics
হা হা হা,0,politics
তোরা জঙ্গী বীরদি না তোরা হচ্ছোছ ইসলাম বীরদি,0,politics
আওমেলিগ ভারতের দালালদের আল্লহর গজব পরুক,0,politics
অপু আপা কি বুকে দম নিয়ে বলতে পারবেন উনার স্বামী জনগনের ভোটে নির্বাচিত হয়ে এম পি হয়েছেন।,0,politics
এই মহিলার ওবোদ সরকার এর । পাগল মহিলা তাকে কানে দরে িপটানো দরকার,0,politics
আওয়ামিলিগ মিতার রাজা,0,politics
কোনো আসবেনা প্রশাসনিক সুস্থতা,0,politics
আপনাকে আলোচনা করার জন্য ধন্যবাদ। ভিডিও প্রতিনিয়ত চাই।,0,politics
এই উদ্দক এর জন্য হাসিনা কে ধ্যনবাদ,0,politics
অপু আপা।।। একটু থামেন কথা তো আসতেছে না তাও কেন মিথ্যা জোর করে আনছেন??বাংলার ইতিহাসে প্রথম শেয়ারবাজার চোর আওয়ামীলীগ আপনি কি জানেননা???,0,politics
খোঁজ নিলে জানা যাবে কাদেরের আন্ডার ওয়্যারের দাম লাখ টাকা। আর উনাকে মানুষ কাউয়া বলে ডাকলেও উনি আসলে লিখেছেন গাঙ্গচিল নিয়ে,0,politics
অপু উকিল আপনি বড় মিথ্যাচার,0,politics
এগুলা জারা করে তাদের জনমের ঠিক নাই এরা মানুসের জনমো না এরা অমানুসের জনমো,0,politics
সবাই কে দিয়ে ভোট চুরি করে নিয়ে এখন খেলা শুরু করছে,0,politics
এইসব বালের খবর আপনি রাখবেন। ফালতু,0,politics
এগুলা তমা ট্রেডার্স এর কামাই মনে হয় । তাতে আপনার কি?,0,politics
আমি থেকে আপনার ভিডিও দেখি।ভাই একটা কথা আওয়ামীলীগের দোষ আছে কিন্তু বিএনপি রা আপনার ভিডিও দেখে খুব খুশি।কিন্তু বিএনপির অতীত আরো জঘন্য। খালদেয়া জিয়ার সরাসরি ভিডিও আছে যে ক্ষমতায় আছি দেশ লুটে খাবো।সব শেষে আমরা মানুষ ভুল সবার ই আছে। কিন্তু কার বেশি সেটা বিবেচনার বিষয়,0,politics
এরা পরতে এসে রানিতি করার কি দরকার,0,politics
আসল তথ্য তুলে ধরেছেন।,0,politics
সোহেল তাজ কে সাধারণ সম্পাদক হিসেবে দেখতে চাই সৎ মেধাবী রাজনীতিবিদ ।,0,politics
চোরের মার বড় গলা। রাজাকারের মেয়ে কয় কি! !,0,politics
ভাইরে এইখানে কি সুটিং ছলে,0,politics
অপু পাগল আমি লিখ ছাগল ছোট মুখে বড় বড় কথা বলে দেশের জনগণ কেন ভোট দিতে পারে নাই।,0,politics
এটা হাইস্যকর ! বাংলাদেশের মানুষের জন্য এটা হাইস্যকর 😂,0,politics
ইনশাআল্লাহ বিচার একদিন হবে,0,politics
জনগনের লাইসেন্স দেখার আগে নিজের লাইসেন্স বানান আপনি,0,politics
আয় হায় হোগায়েদুল সাহেবের কি হবে?,0,politics
বাংলাদেশ এগিয়ে যাচ্ছে ✌✌✌✌✌✌✌✌,0,politics
ফারহানা আপা মদ খান নাকি আপনি???,0,politics
একদম ভইরা দিলেন ভাই,0,politics
সবাই চুদে উবাদুল চুদলে দুস কি,0,politics
জনগন আর ওবায়দুল কাদেরকে দেখতে চায় না। পরিবর্তন দরকার,0,politics
জনগনের টাকা মেরে ঘড়ি লাগাইতাছো।। আল্লাহ তোকে কবে যেন তোর ঘড়িতে তোকে বারোটা বাজিয়ে দেয়,0,politics
কাউয়া ভায়ের নাটক আর দেখতে মনে চায় না।,0,politics
অপু একটি মিথ্যাচার করছে ওকে জুতা পেটা করা উচিত,0,politics
আপু আপনি পারেন এই আঃলীগ হারামির বাচ্চাদের সাতে কেনো জে বসেন এই আঃলীগ হারামিদের সাতে বসলে লাটি নিয়ে বসবেন,0,politics
সত্যি কথাগুলো বলার জন্য আপনাকে অনেক অনেক ধন্যবাদ দোয়া করি আপনার জন্য,0,politics
কিসের শাতে কিসের তুলনা হস্যকর,0,politics
উনি মেম্বার ও হতে পারবেন না,0,politics
লায়লাতুল সরকার বলে কথা🤪,0,politics
শুধু এইকথা গুলোর জন্য অপু উকিলকে নোবেল পুরষ্কার দেয়া উচিত।আচ্ছা বাংলাদেশ থেকে নোবেল পুরষ্কার দেয়া যায়না? না মানে আসলে শুরু করা দরকার।,0,politics
মন্ত্রী পুরা খাড়াশো । হা হা হা হা,0,politics
ভাই আমি আপনাকে আরেকটি নিউজ দিচ্ছি আওয়ামিলীগের একজন ইউনিয়ানের একজন প্রচার সম্পাদক বিয়ে করেছে হেলিকাপ্টার দিয়ে আপনি দেখেছেন নাকী জানিনা তবে যদি না দেখে থাকেন তাহলে একুশে টিভির ওয়েফ সাইড থেকে দেখে আসতে পারেন নিউজটি দেখে কিছু কথা বলবেন আসা করি অপেখ্খায় থাকলাম পরবর্তি ভিডিওটি দেখার জন্য ধন্যবাদ ভাই,0,politics
কায়া বলেছে ঠিক বলেছে যে এক মুখে দুই কথা বলে তাকে কায়া বলায় সায়া ভাবিক,0,politics
ধন্যবাদ জনাব ভাল লাগল,0,politics
আল্লাহ ভালো জানে জোদিও এরকম হয় তাহলে এদেরকে জারা বোট দিবে তারা নাস্তিকের দল ওরা মুনাফিক বেইমান এদেরকে পিটিয়ে দেশ তাড়া করতে হবে,0,politics
ভাই নুর তোর পাসে আমার দরকার রে,0,politics
মন্ত্রী মহোদয় অভিযান করে আর পাবলিক তার পিছনে পিছনে কি জন্য ঘুরপাক করে। অভিযান শেষে কি জিলাপির আশায় এই আম পাবলিক ঘুরে নাকি। বাঙলী তো আবার এক কাপ চা এর বদলে তার মূল্যবান ভোট দিতেও কার্পণ্য করে না। এই হলো আমরা বাঙালি। জিলাপির আশায় কেমন ভিড় পড়ছে। এই দেশের জনগণ যে টাকার বদলে তার সন্মান টুকুও দিতে প্রস্তুত। লোভী এক জাতি।,0,politics
এটা ঠিক না,0,politics
সব নাটক,0,politics
ভাই বুকে আসেন একবার জরিয়ে ধরি আপনকে,0,politics
আললা তুমি নুর ভাইয়ের উপর ছায়া দাও,0,politics
যে শিক্ষা প্রতিষ্ঠানের শিক্ষক মিথ্যা বলতে অভ্যস্ত সে প্রতিষ্ঠানের ছাত্র-ছাত্রীদের দ্বারা আর কি আশা করা যায়?,0,politics
সত্য বলেছেন আপনিও যে গত নির্বাচনের আগে আওয়ামীলীগের চাটামি করে ভিডিও দিতেন সেগুলাও সাধারন মানুষ ভুলে গেছে। প্ল্যান ঠিক আছে এগিয়ে যান দেখবো কতদুর যেতে পারেন।,0,politics
আল্লাহ আওয়ামিলিগ যদি পাঠাইলা তাহলে শয়তান কেন বানাইলা।,0,politics
কি শুরু হইছে বাংলাদেশে ছাগল দিয়ে খেত চাষ করার গল্পটা আজ সত্ত্য করার চেস্টা,0,politics
এর জবাব একদিন দিতে হবে কাদের সাহেবকে এই টাকা সব জনগণের টাকা কৃষকরা ধানের ন্যায্য মূল্য পাইনা।। কত মানুষ দেশে অসহায় কত শিক্ষিত ছেলে আজ বেকার আর আপনি দামি ঘড়ি ব্যবহার করে। আমরা দেখেছি জনাব সৈয়দ আশরাফ সাহেব কি ভাবে জীবন কাটিয়েছেন।,0,politics
কনো কাজ নাই তুদের,0,politics
বুজলামনা কোন পগলে খাদের সাথে কাওয়ারে মিলায় আরে পগলরে গুস্টি তোর পুরা আওয়ামীলীগের সবাইকে এক করলেও খালেদার এক আংগুলে সমান হবেনা,0,politics
বাংলার এইটা পাশ করা প্রধানমন্ত্রী । মুর্করা মুর্ককে অনুসরণ করবে । কথায কাদের অার কথায বেগুন ।,0,politics
কারন ওরা যে এভাবে করে চলছে ওদের ষড়যন্ত্রের ঘাটি এক জায়গায় জমিয়ে রেখেই এমন অঘটন ও পরিস্হিতি চালিয়ে যাচ্ছে।,0,politics
বি আর টি সিস্টেম ঠিক করেনা কেন আমার হারিয়েজাওয়া লাইছেঞ্চ তুলতে দিছি এক বছর হতে জাচ্ছে কারড প্রদান করে নাই এটা কেমন নিয়ম হলো এটা নিয়ে কিছু করা জায়,0,politics
কি যে শুরু হইছে কোথায় খালেদা জিয়া অার কোথায় কাদের অালী ব্যাপারটা হাস্যকর,0,politics
জয় বাংলা।,0,politics
ব্যবসায়ী তো বটেই চেতনা ব্যবসায়ী ।,0,politics
নমিনেশন দিচ্ছে,0,politics
অবৈধ বিনাভোটের গভীর রাত্রে দলবাজ পুলিশদিয়ে ভোটচুরি কারি নিলজ্জ সন্রাসী খুনি কাউয়া কাদিরা দেশথেকে লুটেপুটে খাচ্ছে।। চোর বাটপার দোকাবাজ ঘুমখুনি ভুয়া অবৈধ কাউয়া কাদিরাকে গনদৌলাই দিন।।,0,politics
কাদের ভাই তেও আছে তেও আছে ।,0,politics
অামার একটা অাইন বিষ নিয়া কতা চাই বরত মান সরকার অর একটা করা দরকার অাছে যারা মানুষের গড়ে ডুকে চুড়িি ডাকাতি করে এবং মানুষ খুন করে টাকা পয়শা নিয়ে যায় তাদের বিরুদে অাইন করা উচিৎ জরি মানা বছের জেল লাক টাকা জরি মানা তাহলে দেশর মানুষ শানতি পাবে,0,politics
দেশে এত মুরুক্ষ হার বাড়ছে কোথায় শেখ সাদী কোথায় ছাগলের লেদি সব জায়গায় নাশকতা কা কা কা কা কাউয়া,0,politics
বিএনপি বিবেকবান আওয়ামিলীগ আসল সয়তান,0,politics
শালা একটা বড় অভিনেতা,0,politics
কার কাছে বিচার দাও,0,politics
হাছানুল হক তো রাজা কার,0,politics
ছি ছি ছি কি বলবো ভাষা হারিয়ে ফেলেছি,0,politics
লোক দেখানো আমরা সাধারন মানুষ এগুলো বুঝি,0,politics
অপু ওকিল আওমী লীগ পাগল। নিবাচনের বাংলাদের নিবাচনের মত আর নিবাচন হবে কিনা।পাগল অপু ওকিল একটা পাগল মানুষ হাসে এপাগলে কথা শুনে।,0,politics
ছাত্ত লীগের রগ বাকা,0,politics
মানে মিছা কথা কইতে কইতে দলের কর্মীকে এত চাপাবাজ যে বানাইছে শেখ হাসিনা তো আগে তো জামাতের পাও ধইরা ছিল দেখছে যে যখন যে দুর্নীতিবাজ শয়তান আওয়ামী লীগ জামাত ইসলাম তখনই সরে গেছে আর এখন তারা রাজাকার যে কথায় আছে না পা চাটা গোলাম আমি লীগ যারা করে তারা হল পাচাটা গোলাম,0,politics
এটা সন্ত্রাসী লীগ এর কাজ,0,politics
জারে দিয়া বুত ছারাইবা তারেই দরছে বুতে বিচার দিয়া লাব নাই এই দেশে,0,politics
সবাই পায় সোনার খনি আমি পেয়েছি চোরের খনি! বানীটা সয়ং বঙ্গবন্ধু সেখ মজিবুর রহমানের। চোরের খনি আওয়ামীলিগ এটা তো বঙ্গবন্ধু বলেগেছেন।,0,politics
বিশ্বরেকর্ড আমাদের বিশ্বনবী হযরত মুহাম্মদ সাল্লাল্লাহু আলাই সাল্লাম বছরে তিনি একটা মিথ্যা কথা বলেননি।,0,politics
বিশ্ববিদ্যালয়টা আর এখন বিশ্ববিদ্যালয় নয় এটা এখন বেশ্যাবিদ্যালয় হয়ে গেছে,0,politics
ভালো লাগলো,0,politics
এরা ছাত্রলীগ নামে কঙ্লক,0,politics
দেশ ধবংস কারী লীগ।,0,politics
ভাই কাদেরের ডাবিং টা অসাধারণ হয়েছে🤣🤣🤣🤣🤣,0,politics
ভিডিওটি দেখে সাব্সক্রাইব কইরা দিছি ।,0,politics
বেইমানেরা কথা বলতে পারেনা। হয় তারা আমতা আমতা করে নয়তো বা উত্তেজিত হয়ে যায়। অপু তোর কোন যোগ্যতা নাই রুমিন ফারহানার সাথে এক টেবিলে বসার।।,0,politics
জে দেশে বিরোধী কথা বলে তার মুখে এই কথা মানায় না,0,politics
সড়ক কাদেরের সাথে ভ্যাদাইমার ও তুলনা চলেনা।,0,politics
কততা লিগ এক দিন বুজবি,0,politics
বাংলাদেশের গর্ব জনাব ডঃ হাসান মাহমুদ স্যারকে অাওয়ামী লীগের সাধারণ সম্পাদক পদে দেখতে চাই।,0,politics
কাওয়া মুনাতীরি লুচা,0,politics
চুরের মায়ের বড় গলা,0,politics
ভাইয়া আপনার ভয়েসটা অনেক সুন্দর,0,politics
স্যার তো পুরাই মুখ্য,0,politics
বোদা এক চাকা মুলা এক চাকা,0,politics
ছাত্র ছাত্রীরা বিশ্ববিদ্যালয় পড়াশুনা করতে আসেন না এরা শুধু নোংরা রাজনীতি করতে আসে। এরা নাকী দেশের ভবিষৎ কর্ণধার।,0,politics
কাওয়া ডারে স্পিচথেরাপি দেয়া উচিত,0,politics
হেতে মনে হয় মিঠন এর চবি দেখছে,0,politics
অপু মিথ্যা বাদি,0,politics
সরকার নিশ্চপ কারণ মিয়া ভোট দিয়ে জন প্রতিনিধি নিবাচন করছিলি নাকি? যার জম্ম অভদ্য তার কাজ অভদ্র হওটা সাভাবিব না ভাই,0,politics
কাদের সাহেব কোটি টাকার ঘড়ি আর আমার টাকার ঘড়ি একই সময় প্রদশন করে। আমার প্রশ্ন হচ্ছে দুদক কি কলা গাছ নিয়ে ব্যস্ত??? কারন কলা গাছ ছাড়া তাদের চোখে কিছুই ধরা পড়ে না।,0,politics
ইনু তোর বিচার জনতার আদালতে হবে,0,politics
এদের দ্বারা যে দেশ চলে যে দল চলে তাদের কী অবস্থা হতে পারে! সবই অশনিসংকেত!,0,politics
আমি নুরুকে অনেক পছন্দ করি কিন্তু মেয়েগুলোর কি লাজ লজ্জা নেই এই গুলোর কি বাবা মা নাই এই গুলো কি ছেলেদের ধাক্কা না খেলে কি শরীলের জ্বালা কমেনা।,0,politics
এ সিক নাকি?? না মানশিক রোগী?? কথা বলার সময় এ নাকে কানে হাত দেই শিশু আর পাগলের মত।,0,politics
জাহাঙ্গীর কবির নানক কে সাধারন সম্পাদক বানানো হোক,0,politics
বাংলাদেশের সাধারণ মানুষকে বোকা পাইছো? হাতে ক্ষমতা পেয়ে যখন যা খুশি করতে মনে চাইবে তাই করবে ? না তোদের সময় বেশি দিন নাই। ফাটা কেষ্ট সাজতে চাও না তা কখনই হবে না। দিন দিন তোদের অত্যাচারে দেশের সাধারণ মানুষ অতুষ্ট হয়ে যাচ্ছে মানুষের দোয়ালে পিঠ ঠেকে যাচ্ছে। মানুষ ক্ষিপ্ত হয়ে গেলে তোদের বাচার উপায় নাই।আমি কারও বিরুদ্দে কখনওই বলিনাই বলার মতো ভাষা আমিও জানি আজ তোকে আর তোর মা হাসিনাকে বললাম। মনে রাখিস আমার মতো আরও যারা এদেশে আছে তাদের যদি একবার মট্কা গরম হয় তখন কিন্তু ঠ্যালা সামলাতে পারবিনা। এখনও সময় আছে সরকারের চাটুকারীতা বাদ দে। আমি আজ এসব কথা বলতাম না তোকে এরকম কাজ করতে দেখ না বলে পারলাম না।,0,politics
অাওয়ামী লিগ মানেই নির্লজ্জ।,0,politics
এতো ভালো মানুষ এখনো আছে ইসস রে,0,politics
চোর,0,politics
কিছুই হবে না ভাই,0,politics
অপু উকিল তো একটা বেয়াদব,0,politics
অামি অাছি যতো দিন খেয়ে যাবা ততদিন হাসু অাপু সরকার বার বার দরকার লিখছি অামি কাউয়া কাদের,0,politics
হাস্যকর অপুকিল! কৈ কাওয়া কাদিরা আর কোথায় বেগম জিয়া। ধারুন জবাব দিয়েছেন ব্যারিস্টার রুমিন। বেগম জিয়া আর বাংলাদেশ টোই একে অপরের পরিপুরক,0,politics
বাংলার মাঠি থেকে ছাত্রলীগ ক্যান্সার উপড়ে ফেলতে হবে! তরুন প্রজন্ম চরম ক্ষেপতেছে!!,0,politics
কোথাই খালাদা জিয়া আর কোথায় কাদের ! বেপারটা হাসক্যর,0,politics
জনাবা অপু উকিল আপনার কথা শুনে মনে হয় বাংলার সেই আদি বাক্য চোরের মায়ের বড় গলা😠,0,politics
দিদির তার চিরা রুমিনথেকেে সিখ কথা কি ভাবে বলতে হয়,0,politics
সব সময় আপনার ভিডিওর অপেক্ষায় থাকি🙏🙏🙏,0,politics
দেশে কি হলো এই শালী কি মরণের ভয় নেই। ভাইরে আমার কাছে যদি একটা পারমানবিক থাকতো ।সবাই কে উড়িয়ে দিতাম।,0,politics
আয় ভাই বুকে আয় আমার বুকে আয়।,0,politics
এগুলা রেপ্লিকা আর গিফটের,0,politics
এইরকমেই হবে। এইরকমেই চলবে। কিছুই করার নেই। আল্লাহ কে ডাকতে হবে। আল্লাহ যেন আমাদের কে হেপাজত করে।,0,politics
কাদের সাহেব যা ব্যবহার করেন তা হলো দেড়শত টাকার কপি মাল!! দূর্নীতি কাকে বলে কত প্রকার কি কি সব দেখিয়ে দিচ্ছে!!,0,politics
ওবাইদুল কাদের খালেদাজিয়ার একটা বালের সমান হবেনা,0,politics
তার পরও বাংলাদেশের মানুষ বিশ্বাস করতে চায় না যে বাংলাদেশ কত উন্নত দেশে পরিণত হয়েছে ! আমরা এই জন্য গর্বিত যে কাদের ভাই প্রেসিডেনট ট্রাম্প এর কাছাকাছি চলে গেছেন !!,0,politics
সৈয়দ আশরাফ একজন ভালো ব্যক্তি ছিলেন৷ কিশোরগঞ্জের গৌরব ময়মনসিংহের গৌরব।❤❤❤,0,politics
ভাইয়া সাউন্ড সিস্টেমটা আরেকটু ভালো হলে ভালো হতো।,0,politics
নতুন পাগল দেখা গেছে,0,politics
কতো নাটোক দেখতে হবে যানি না সে হিরো হতে চায় কাউয়া,0,politics
এদের কে জুতা দিয়া পিঠাও সবাই,0,politics
বিএমপি করা বাত দে,0,politics
কাদের সাহেবের জনপ্রিয়তা সামাজিক যোগাযোগ মাধ্যমের কমেন্টস দেখলেই বুঝা যায়।,0,politics
হাসানুল হক ইনু এবং রাশেদ খান মেননকে আর মন্ত্রীত্ব দেয়া উচিত হবে না। কারন ইনু বংগবন্ধুকে নিয়ে অনেক কটু উক্তি করেছে। সে একটা মীর জাফর।,0,politics
চুরি মিলেমিশে চুরি ভালই করেছো চেতনা ব্যবসায়ী মীরজাফর ।,0,politics
ভাই আমরা সবাই আছি আপনাদের সাথে বিএনপি,0,politics
এসব হাস্যকর কথা শুনলে মনে হয় কি যে করতাম আসলে এই সরকারের আমলে এসব কথাশুনাও সাধে,0,politics
জনগণের পাছায় বাশ দিয়ে জনগণের টাকা লুটপাট করে এত বিলাসিতা করে।,0,politics
বাঘের সাথে ✔️ ।।।।🤣🤣🤣 বিলাই এর তুলনা। ।।।,0,politics
সালার তুদের কাজ নাই,0,politics
এখন উনি ঘড়িকেষ্ট 😂,0,politics
পড়াশুনা শেষ করে রাতদিন পরিশ্রম করে টাকা বেতনের চাকরি করতেছি। আর কাদিরা হালারফালা !!!!!,0,politics
ওবায়েদুল কাদের যদি দুনিয়ার সব টাকার মালিক ও হয়ে থাকে আপনার আমার কোন লাভ নাই।,0,politics
সাংগাতিকরা অনেক জামেলা করে,0,politics
আমি স্বাধীন দেশের বাক পরাধীন নাগরিক কিছুই বলতে পারছি না শুধু এতটুকু বলছি ভাই অবিরাম ভালোবাসা,0,politics
ভাইয়ের জন্য দোয়া রইল,0,politics
কাদেরকে বাদ দিলে ভালহবে। উনি ফেনীতে আওয়ামীলীগকে্ ধংশ করে দিচে।,0,politics
নাউজুবিল্লাহ,0,politics
মুবাইল টি নিজের টাকা কিনা,0,politics
এসব শিক্ষক এর জন্মেতে সমস্যা আছে,0,politics
দেশটারে হুগা মাইরা দিতাছে বাকিটা ইতিহাস,0,politics
কাক আর কোকিল কি এক,0,politics
দালাল,0,politics
খালদা জিয়ার শিপন শাড়ি নিয়ে এর পর প্রতিবেদন করুন🙄🙄,0,politics
আই ওয়াস,0,politics
অপু চুন্নি,0,politics
স্যার বাংগালীতো,0,politics
আমি আওয়ামী ছাত্রলীগের কর্মী। আজকে থেকে দল ছেড়ে দিলাম।এরকম দেশে আমার জন্ম ছি ছি ছি। ভিপি নুর সাথে আছি তোমার ইন্সাল্লাহ । তোমার কিছু হলে এই দেশে আবার যুদ্ধ হবে ইন্সাল্লাহ৷,0,politics
এরা সবাই তো এখন হাতে থালা নিয়ে বসার অবস্থা।,0,politics
আমরা লজজা বিহিন হাছিনার পরিবরতন চাই ভোট চোর হাছিনা কাউয়া কা কা করিস নারে,0,politics
খালেদা জিয়ার সাথে কাউয়ার তুলনার প্রশ্ন আসাটা অযোক্তিক খালেদা জিয়া সাথে কাউয়া কেন ভোট চোরাই প্রধানমন্ত্রীরও তুলনা হতে পারে না।,0,politics
সরকারের ওচিত জারাই টাকার লোভে দলকে সমালচনার মুখে ফেলে তাদের দলথেকে দূরেইরাখা।,0,politics
তোমার সাহস দেখে অবাক হইলাম। 💞,0,politics
আপনি তো আয়া মিলিগের দালাল,0,politics
আলহামদুলিল্লাহ শেখ হাসিনা বাদে আর সব খারাপ। এজন্য প্রয়োজন সৎ ব্যাক্তি।,0,politics
তোমাকে হাজার সালাম ভাই,0,politics
ভাই এগু‌লো গিফট্ এর ঘ‌ড়ি!,0,politics
ওবায়দুল কাদের গাড়ি নিয়ে তোমার সমস্যা কি,0,politics
সবার দৃষ্টি আকর্ষণ করছি। বিশেষ করে প্রধানমন্ত্রীর। বাঙালিদেরকে পাকিস্তানিরা বহুত অত্যাচার নির্যাতন করেছে। কিন্তু যতই কষ্ট হোক পরিশেষে জয়টা কিন্তু বাঙালিদেরই হয়েছে।তাই সাবধান আপনার এইসব কুলাঙ্গার ছাত্রলীগের ছেলেমেয়েদের সৎ পথে নিয়ে আসুন। কারন সময় আর বেশি নাই আপনার পতনের। সম্মানের সাথেই যাতে অবসরে যেতে পারেন। কারন আমরা আর আপনাদের কাউকেই চাইনা। নতুন মুখ দেখতে চাই। অতিষ্ঠ হয়ে গেছি আপনাদের এইসব ভন্ডামি ব্যবহারে।এর থেকে বেশী সম্মান করতে পারবোনা।নজর দিন সাধারণ মানুষের সুযোগ সুবিধায়।আর দেশের জনগণের গণতান্ত্রিক অধিকার ফিরিয়ে দিন।দেশটা আপনার একার না যে আপনার একান্ত ইচ্ছামত চলবে। আমাদের সবার সমান অধিকার এই দেশের। আমাদের মতো সাধারণ মানুষের প্রাণের বিনিময়ে অর্জিত আমাদের এই সোনার বাংলাদেশ।,0,politics
আরেক মাদারবোর্ড হানিফ আছেনা কাদিরাকে সরাইলে হানিফ নিশ্চিত।,0,politics
এই কুকুরদের কোন বিচার হবে না,0,politics
হাহাহাহা,0,politics
আওয়ামীলীগ এখন দেউলিয়া হয়ে গেছে আওয়ামীলীগের আগা গোড়া ঠিক নেই তাই বাংলাদেশের সবচেয়ে জনপ্রিয় নেএী ও তিন তিন বারের প্রধানমন্ত্রীর সাথে জন ফাটা ছেড়া লোকের তুলনা করে।,0,politics
অপু কে পেলে জুতা পেটা করা উচিত,0,politics
ভাই অনেক ধন্যবাদ এরা অামাগো ফকির কইরা দিলো।,0,politics
সাধারণ সম্পাদক জাহাজ্ঞীর কবির নানক ভাইকে দিলে ভালো হবে।,0,politics
ভিপি নুরের সাথে যারা ছাত্র ছাত্রী আছো তার সবাই নিজেদের নিরাপত্তা জন্য যা যা দরকার তাই হাতের কাছে রাকবা ।,0,politics
ছোট ও আপা কই!?,0,politics
বদল করলেই কি আর না করলেই কি! সব চোরের দল,0,politics
কোথায় লিভারপুল অার কোথায় ফকিরাপুল 😀,0,politics
না ভাই আমাদের স্বভাব টাই এরকম। কই আপনি যদি তাদের ভাইকে এতই ভালোবাসতেন সম্মান করতেন কাদের ভাইকে নিয়ে কেউ ট্রল করলে আপনার এতই যদি খারাপ লাগতো তাহলে এই কথাগুলো আগে বলেন নাই কেন। যখন সে ভালো কাজ করতেছিল তখন আপনার শুধুই ভালো লাগতো! কই তখন তো এগুলো নিয়ে কোন ভিডিও বানানোর প্রয়োজন মনে করেন নাই? ঠিক তখনই আপনার ভিডিও বাড়ানোর প্রয়োজনীয়তা মনে পড়ল যখন কিনা তিনি গিফট পাওয়া ঘড়ির নিয়ে গনমাধ্যমের সমালোচনার মুখে পড়ল।,0,politics
আমাদের সোনা এখন বাংলা ছবি দেখে না ‘,0,politics
আওয়ামীলিগ হচ্ছে বিনোদন লীগ😀😀,0,politics
এই ঘড়ি গুলো অবশ্যই বি এন পি জামায়াত তাকে জোর করে পরিয়েছে। মুক্তিযুদ্ধের চেতনা নেই বলেই তারা কেসিনো বেবসা না করে একজন কাউয়া র পেছনে লেগেছে,0,politics
এটাই হল উন্নত বাংলাদেশ,0,politics
ভাই আপনি একটা মাল। খুব ভালো লাগে ভাই,0,politics
সেই ভাই,0,politics
ভাইরে এত মিসা তোরা কেমনে কস? তোরা যদি লজ্জা শরমের উদ্ধে যেয়ে রাস্তায় ল্যাংটা হয়ে হাঁটিস আমরা দেখি কোন লজ্জায়?,0,politics
ডিম একন খাওয়া যাইবনা,0,politics
খা‌লেদা এখন জে‌লে এখন গা‌লি গালাজ এর প্র‌য়োজন না তাই তো‌রে এখন দরকার নাই সেখ হা‌সিনা বু‌ঝে‌গে‌ছে,0,politics
আপনি একটা জিনিস,0,politics
আমার দেখা রাজনীতি ব্যক্তিদের মধ্যে সবচেয়ে বেশি পা চাটা লোক হচ্ছে ওবায়দুল কাদের। মনে হয় না নতুন কেই আসবে। কারণ পোষা কুকুরের ন্যায় কাদের।,0,politics
কথায় বলে।কোথায় ঈন্ধিরাগান্দি আর পাছার ফান্দি।,0,politics
জোর করে ঐক্য রাখতে চাও। তুমার মত ইনু না থাকলে আওয়ামীলিগের কোন কিছু আসে যায়না। বাংলাদেশে ইনুর মত লোকের কোন মুল্য নাই।,0,politics
ওবায়দুল কাদেরে কেউ আইডল মানতে পারে এই ভিডিও না দেখলে জানতাম না🤐🤣🤣,0,politics
ছি কি হতেছে,0,politics
খুবই কম দামি ঘড়ি,0,politics
আল্লাহ্ তোদের বিচার করবেন,0,politics
আমাদের বড় সমস্যা হলো আমরা কেউ বিপদে পড়লে এগিয়ে আসে না।মরার আগে মরে দেখার এই সাহস টা আমাদের নাই,0,politics
সবার কাছে খালি টাকা আর টাকা,0,politics
কাউয়ার সাথে তুলনা!!!,0,politics
এনা পরিবহনের সেয়ার হোলডার সে যত টুকু শোনা যায়। আর এরকম একজন রাজনৈতিক এর এরকম ঘড়ি থাকতেই পারে।,0,politics
বাইরের দেশের কোনো মন্ত্রী এমনটা করলে বাহবা দিই কিন্তু এটা তো নিজের দেশ। তাই সবাই চামচা আর দালাল বলে।আগে নিজেকে একটু পাল্টায় ভাই,0,politics
কোথায় লিয়াকত আলি আর কোথায় জুতার কালি ওবায়দুল কাদের খালেদা জিয়ার জুতা মুছতে দেওয়া হবে না।,0,politics
এই ঘড়ির টাকা কি তার বাবার দেশের আর কতো করে খাইবো সরি আর কিছু বুলার নাই,0,politics
ওবায়দুল কাউকে কেউ কি ভোট দিয়ে মন্ত্রী বানিয়েছে সে তো জুলুম নির্যাতন করে অবৈধভাবে ক্ষমতায় এসে হাসিনার পা চাটে এখন মন্ত্রিত্ব করতেছে দেশটাকে সর্বনাশে ঠেলে দিচ্ছে। আর সে কাউকে বাংলাদেশের তিনবারের প্রধানমন্ত্রীর সাথে তুলনা করা হচ্ছে সেই আমি এই সমস্ত মন্তব্যকারীদের কে ধিক্কার জানাই তাদের মুখে থুথু মারি,0,politics
অপুর কথা সব মিথ্যা।এবংটাউট।,0,politics
আজ কাল সত্যি কথার ভাত নাই সত্যি বললে মার খাইতে হবে,0,politics
তেলাপোকাও একটা প্রানী আর কাউয়াও একটা মন্ত্রী আগের দিন খালেদা জিয়াকে নিয়ে কুটকতি করেছে ঠিক তার পরের দিনই কাউয়ার উপরে আল্লাহর গজব পরেছে।।,0,politics
হায় হায় কাদের কাক্কুর কি হপ্পে?😆😅😂,0,politics
এদেশে সঠিক বিচার পাওয়া যাবেনা আমার মনে হয়।তবুও দোয়াকরি নুরূ ভাই সত্যর জয় হয়,0,politics
রাজাকার তো আওয়ামীলীগেই বেশি👍 ও সরি ওরা তো এখন মুক্তিযোদ্ধা 🤣🤣😜,0,politics
ইনু তোমার গিতাপাটের দিন শেষ এখন পিঠে ছালা বন্দ। পাগলা কা কা করে লাভনাই।,0,politics
উনার মানসিক সমস্যা আছে। না হলে একজন মিনিস্টারের কাজ এটা না। হে লাইসেন্স চেক করে আর হাজার হাজার মানুষ ভোগান্তিতে ভোগে।হালা আবাল। লোক দেখানোর কাজ বন্ধ করুন।জনগণ আপনাদের ভালো করেই চেনে,0,politics
আমিও মাঝে মাঝে আমার লেজের মধ্যে ঘরি লাগাই।। আমার ঘরির দাম মাত্র টেকা,0,politics
তার ত নিজের লাচেচ নাই ইনি কি লাচেচ চেক করে,0,politics
পাঁ চাটারা কেমরা নিয়া কি করতাছে জে দিন সাধারন ছেলে মেয়ে দের উপর হামলা হলো সে দিন ওরা কোথায় চিলো।,0,politics
সর্ব প্রথম ওবায়দুল কাদের হাসান মাহমুদ সাজাহান খান কামরুল ইসলাম এইচ টি ইমাম এদের পরিবর্তন করতে হবে তাহলে অন্তত আওয়ামিলীগের ইজ্জত কিছুটা হলেও রক্ষা করা যাবে,0,politics
তোদের কি এটা বাপ দাদার আও,0,politics
জাময়াত আর বি এন পি এর নেতারা এসে পদ পাচ্ছে এতে আওয়ামী লীগ এর ক্ষতি হচ্ছে,0,politics
সকল মন্ত্রীদের হাত ঘড়ির মোট দাম তাহলে কত পারে প্রধানমন্ত্রীর তা তদন্ত করা উচিত??????,0,politics
ভাই আপনাকে আমার মন থেকে ভালোবাসা রইলো আপনার মতো একজন মানুষ আমাদের এই সময়ে খুবই প্রয়োজন ❤❤❤❤,0,politics
নুরু মনে হয় বিয়ে করতে আসছে।,0,politics
প্রধানমন্ত্রী শেখ হাসিনা আগামীতে আরো সুষ্ঠু বিচার করবে সেটাও হাসানুল হক ইনু দেখবে ধন্যবাদ,0,politics
দেশের গুয়া মারা সারা জা ইচ্ছা তাই বলে জাচ্ছে আউয়ামিলিগ। জিয়ার ফেমিলি ইতিহাস,0,politics
কাদের এর সাথে শেখ হাসিনাকে মানায় 😂😂😂 শালার খালেদা কত ও বড় মানুষ,0,politics
আমার সোনার বাংলা কবে যে আওয়ামীলীগ বিএনপি যুদ্ধ বন্ধ হবে ? একই জাতীয় পার্টি দ্যা হিজরা মার্কা দলকে। আর কবে যে এই দুইটা দলকে বাঁশ দিয়ে বাংলাদেশ থেকে তাড়াতে পারবে সেই হবে আসল বাংলার বীর। ভাল্লাগে না দুই মহিলার বাপ স্বামীকে নিয়ে যুদ্ধ। দেশের জনগণ কি দেশের মালিক না ? দেশের মালিক কি বঙ্গবন্ধু বা জিয়াউর সাহেব ? নাকি আওয়ামীলীগ বা বিএনপি ? তাহলে লক্ষ যুদ্ধা কি করছে পাকিস্তানের সাথে যুদ্ধের ময়দানে ?? দেশ তো জনগণের দেশ না। এইটা হয়ে গেছে আওয়ামীলীগের বাপের টাকায় বঙ্গবন্ধু সাহেব আর বিএনপির স্বামীর টাকায় অর্থাৎ জিয়া সাহেব । শেখ মুজিব আর জিয়াউর রহমান তো বলে নাই দেশটা আমার বাপের টাকায় কিনা ? কিন্তু আওয়ামীলীগ আর বিএনপি ঠিকই এই কথা বলে।,0,politics
সবই চোর কি নলবো আর,0,politics
তুলনার কি আ‌ছে এটাই বুঝলাম না।,0,politics
আর পাবলিকের কনো কাজ নাই,0,politics
ইনু তুই রাজাকার বিধায় এ কথা বলতে পারলি।⏰,0,politics
আমি একটা জিনিস বুঝি না।ভিপি নুর ভোট কারচুপি হচ্ছে বলে ডাকসু নির্বাচন বর্জন করল তাহলে কারচুপি করলো টা কে নুর এর লোক নাকি ছাত্রলীগ।আবার ফল প্রকাশের পর এখন বলে সাধারন ছাত্র ছাত্রীদের ভোটে নির্বাচিত ভিপি নুর।হাইরে নাটক।,0,politics
ভাই কালকে আপনার চ্যালেন টাও বন্ধ করে দিতে পারে। এই বাংলাদেশে কেনোকিছু অসম্ভব নয়। আপনি অনেক সাহসি।আপনার জন্য আমার এক বুক ভালোবাসা।💓💓❤❤💓,0,politics
ছাত্রলীগ হাটাও বাচ্চাও দেশ,0,politics
বিনোদন আর বিনোদন বুড়ো বয়সে আমার কত ছবি তুলে আমার কাছে শাকিব খান ফেল মরে কেউ হানির মধ্যে সুবা,0,politics
এরা ভাইরাস এরা যেখানে থাকবে সেখানে মহামারী আকার ধারণ করবে হায়রে বাংলাদেশের রাজনীতি,0,politics
আমগো ছাদ না থাকলে অনেক কিছু মিস হইতো🤣 ভিডিও কিত্নু জোস😍,0,politics
আমাদের বাঁশখালীর এম পি মোস্তাফিজুর রহমান।,0,politics
বাংলাদেশ প্রেমিক বাঙ্গালি জাতি ও জাতীয়তাবাদ প্রেমিক স্বাধীনতার অতন্দ্র সৈনিক ওবায়দুল কাদেরের সাথে বাংলাদেশ বিরোধী বাঙ্গালি জাতি ও জাতীয়তাবাদ বিরোধী পাকিস্তানভিত্তিক স্বাধীনতাবিরোধী সন্ত্রাসবাদি দল বিএনপি প্রধান খালেদা জিয়ার তুলনা হওয়ার কোন প্রশ্নই আসে না। কারণ তুলনা হতে পারে দুটি একই জাতীয় জিনিসের মধ্যে। এখানে দুটি সম্পূর্ণ আলাদা আলাদা জিনিস। একটা দেশ ও জাতি প্রেম অন্যটা দেশ ও জাতি বিরোধিতা দেশ ও জাতির বিরুদ্ধে শত্রুতা। এখানে তোমরা যারা অপু এবং আওয়ামী লীগকে জঘন্য নোংরা ভাষায় গালিগালাজ করেছো তোমরা হলে জিয়াউর রহমান ও খালেদা জিয়ার সন্তান। তোমরা হলে তোমাদের মা বাবা জিয়া খালেদা জিয়ার সার্টিফিকেট। সার্টিফিকেটেগুলিই় পরিষ্কার বলে দিচ্ছে তোমাদের মা বাবা জিয়া খালেদা জিয়া কি ধরনের জিনিস। ধন্যবাদ,0,politics
হা হা হা ভাই আমার সপ্নো গুলো ভেঙে গেল,0,politics
ভাই অামি দোয়া করি অাপনাদের যেন ভালো হয় ছাএলীগ যেন দমন হয়,0,politics
টাকা পাচার করা শেষ জনগনের গুয়ামারা শেষ এখন ডেটল লাগিয়ে লাভকি।,0,politics
শুধু পুঁটি মাছ ধরলে হবে না। বড় বড় বোয়াল মাছ ধরতে হবে।,0,politics
সোনার বাংলাদেশ দেশ এখন চুরের দেশ হয়ছে।,0,politics
কাউয়া কে কাউয়া বলবে না বলবে কি। নাম্বার ওয়ান কাউয়া,0,politics
হাইরে বাংলাদেশ,0,politics
মাসআললাহ্ আর কোথাও জদি নায়েকাদের না পাই আমাদের মন্ত্রী মহাদয়ের জে কোনো মিটিং এ দেখতেপারি,0,politics
এরে ভাই আপনার সামনে অবশ্যই বিপদ।,0,politics
ধংষের নমুনা,0,politics
ওবায়দুল কাদের সাহেব শৎ মানুষ তার সাথে এতিমের টাকা চোর খালেদার তুলনা হয় না,0,politics
ফাটা গলা রে বাদ দিয়া দেন,0,politics
হালা আওয়ামীলিগে দরবেশ আসলেও শ্রেষ্ট মিথ্যাবাদী হয়ে যাবে মাত্র তিন দিনে।,0,politics
কিযে শুরু হয়েছে ভাই তিন তিন বার প্রধান মন্ত্রী,0,politics
গোফ খাটো করিয়েন,0,politics
গু,0,politics
শেখ হাসিনা ছারা যোগ্য প্রধানমন্ত্রী বাংলা দেশ কেউ নাই দেশের উন্নয়নে র সরকার শেখ হাসিনা সরকার ।,0,politics
কোথায় রাজ রানী আর কোথায়,0,politics
সৈয়দ আস্রাফের ইন্তেকাল সংবাদে অত্যন্ত দুঃখ পেলাম ইন্নালিল্লাহি ওয়া ইন্না ইলাইহি রাজিউন । চমৎকার হয়েছে আপনের উপাস্থনা। ধন্যবাদ।,0,politics
খালেদা অনেক বড় কিনতু চোর। কাদের অনেক ছোট কিনতু চোর নয়। চোর চোরি থাকে খালেদা ওচোর তারেক ও চোর,0,politics
অনেক সুন্দর ভিডিও ভাই অসংখ্য ধন্যবাদ আপনাকে,0,politics
ভাই কার সাথে কার তুলনা কি বলবো ভাই,0,politics
কই আগরতলা কই সকির তলা।,0,politics
এখন বললেই হবে না পরে যেন মনে থাকে???,0,politics
আমার টাকার ঘড়িও বরাবর সময় আপডেট দেয়। এ রাজনীতিবিদগুলা আমাদের জনগনের টাকা লুটেপুটে ফুটানি করে,0,politics
আমি বি এন পি সুদিনা,0,politics
ঠিক বলেছেন আপু তুমি অনেক সাহসী নেত্রী বেগম খালেদাজিয়ার কোন বিকল্প নাই,0,politics
যারা এত ভালোবেসে এত দামী ঘড়ি দেয় তারা কেন এ এর খরচটা দিল না? তা হলে তো গরীব প্রবাসীদের পাঠানো টাকা কিছুটা বেঁচে যেত যা দিয়ে এতিম ছেলেদের ঘড়ি কিনে দেয়া যেত ।,0,politics
যারা মানুষের ভোটের অধিকার হরণ করছে তাদের বিচার আললাহর কাছে দিলাম।,0,politics
কই রাজরাণী কই জুতার কালি কই কাউয়া আর কই খালেদা জিয়া,0,politics
ইনু সাহেব এখন পাগল হয়ে গেছে কি বলবে ভেবে পাচ্ছেনা,0,politics
￰কিছুদিন পর ইনু যদি দেশেথাকে পোলাপান ওরে বল বানাবে,0,politics
ওবায়দুল কাদের কাউয়া ভুয়া আল্লাহু ঘজব দিয়ে ওবায়দুল কাদের আল্লাহু বিচার কি ভাবে করে তা এখন সারা দুনিয়া এখন তা সবাই জানে আওমিলিগে উপর ঘজব নাজিল হয়েছে আওমিলিগের লোক মোনাফেক এবং নাস্তিক এদের ধংশো আল্লাপাক করবেন,0,politics
দালাল মিড়িয়ায় এই ধরনের প্রশ্ন করার কি দরকার ????,0,politics
প্রকৃত অর্থে কাদের সাহেবের সাথে খালেদার তুলনা করা ভূল।,0,politics
এই খানে সেনাবাহিনী দরকার,0,politics
কবর থেকে প্রত্যাবর্তন ওকে শখ করতে দিন ।,0,politics
ওদের পালন করছে মা জননী বহিষ্কার কে করবে !,0,politics
আমি লজ্জিত আমার জন্ম বাংলাদেশে নুরু ভাইয়ের জন্য দোয়া রইলো,0,politics
কোথায় রাজরানী কোথায় চুতমারানি,0,politics
উনি তো মানুষ নাহ্ এরা হলেন মতোই ইনু বলেন যে,0,politics
চোরের হাতে দামি গাড়ি,0,politics
ঝালকাঠি জেলার অনুপ্রবেশকারী কি ভাবে এতো সাহস হয় দেখুন ভিডিও। তারা প্রধানমন্ত্রী ও আমির হোসেন আমু ভাইয়ের সিদ্ধান্ত কিছুই মানেন না,0,politics
আসসালামু আলাইকুম আজ আমি কিছু কথা বলতে চাই আমি সরকারি বি এম কলেজের সাবেক ছাত্রী এবং ইডেন কলেজের বর্তমান একজন ছাত্রী।আমাদের দেশের সর্বোচ্চ শিক্ষা প্রতিষ্ঠান হলো ঢাকা বিশ্ববিদ্যালয়।সেখানে আমাদের মতো অনেক ভাই বোন আসে প্রকৃত অর্থে শিক্ষা লাভের জন্যই কেউ সেখানে রাজনীতি বা মারামারি করতে বা কোন মেয়ে যৌন হয়রানির শিকার হতে আসেনা এবং কোন বাবা মাও তার সন্তানকে এই উদ্দেশ্যে ঢাকা বিশ্ববিদ্যালয়ের মতো একটা প্রতিষ্ঠানে ভর্তি করেন না কিন্তু কেন সেখানে এসে আমাদের ভাই বোনদের এই রকম হয়রানির শিকার হতে হবে যা প্রকাশ্যে এবংতাদের মুখেও শুনতে হইতেছে দ্বিতিয়ত আমরা দেখলাম বর্তমান যে ঘটনাটা ঘটলো সেখানে ভিপি সাহেব গিয়ে একটা সমাধান দিতে চেয়েছেন সেখানেও কেন ছাত্রনামের সন্ত্রাসীরা হামলা করেছেন ভিপি সাহেব প্রভোস্ট সাহেবকে সেই ঘটনাস্থলে যাওয়ার জন্য ফোন দিলেন তিনি রিসিভ করলেন না আবার তিনি সেখানে অনেকক্ষণ পরে এসে যখন সাংবাদিকদের সামনে কথা বলছেন তখন তিনি সম্পূর্ণ না বল্লেন যে তাকে ফোন দেয়া হয়নি এই যদি হয় একজন সম্মানিত শিক্ষকের কথা তাহলে আমার কিভাবে ভালো কিছু শিখবো?এসব দেখেতো মনে হচ্ছে দেশের এই উচ্চ শিক্ষা প্রতিষ্ঠানের এই শিক্ষার চেয়ে নিম্ন শিক্ষা প্রতিষ্ঠানে পড়া অনেক ভালো যেখানে থাকবেনা কোন সন্ত্রাসীর ভয় যেখানে থাকবেনা কোন যৌন হয়রানি শিকারের ভয় যেখানে থাকবেনা কোন বড়কোন সত্য লুকায়ে কিছু মিথ্যা কথা বলা আজ খুব খারাপ লাগতেছে যে দেশের সবচেয়ে বড় শিক্ষাপ্রতিষ্ঠান গুলোর অবস্থা দেখে যেখানে নিরিবিলি পরিবেশে শিখতে যাই কিন্তু সেখানে সবসময় কাটাতে হচ্ছে ভয়ে কখন যেন হামলার শিকার হতে হয় এর থেকে প্রতিত্রান পাওয়া দরকার যাতে ভবিষ্যতের কর্ণধার যারা আসবে তারা যেন এই সমস্যায় না পড়ে আর বাবা মায়েদের কোন টেনশন না করতে হয়,0,politics
কোথায় রাজরানী আর কোথায় চুদমারানী ?,0,politics
বাংলার বাঘিনী রুমিন ফারহানা সাববাস,0,politics
আওয়ামী লীগতো ভোট চোর তাই ওবায়দুল কাদের মুখে সুনি আওয়ামী লীগ চারা আর কোন দলে জিতে পারে না এই কথা বলতে পার শুধু ভোট চোরেরা,0,politics
ইস্কন আলম ভাই কেমন আছেন???ইস্কনের দালালি করবেন না???,0,politics
তারপর ও লজ্জা হবে না তাদের,0,politics
নত্যকিদের কে নিয়ে এতো আন্দ,0,politics
শেখ হাসিনা কি কম বিতকিত হয়েছে নাকি একটা কথা কেনো আওয়ামীলীগ করেনা নামে গনতান্ত্রিক দল না বলে এক কাজ করলে হয় জে আমরা থাকবো আজিবন ক্ষমতায় কারো হাতে দেবনা দেশ কারন দিলে দেশ কারো হাতে বাজবে বারটা আওয়ামিলীগের অন্যায় জে করছে বেস তাই তার বিচারের নেইজে সেষ টাইবুনাল করলো জামাত বিএনপির জন্য সেই টাইবিনালে হবে বিচার আওয়ামীলীগ বলেছিলাম সবার দেবো সম্পদের হিসাব গতো হলো দশ বছর দেই নাই সেইসাব শেয়ারবাজার খেলাম খেলাম মানুষের রক্ত রানামারলো শো মানিষ রানা থাকে জামাই আদরে কর্নেল তারেক মারলো জন তারেক গুমায় এসি রুমে জোসেফ হলো খুনির আসামি জোসেফ জায় বিদাশে এমপি লিঠন মারলো মায়ের পেটের সন্তান সেই এমপি লিঠন ও পেয়ে জায় রেহাই ঘন্টার আসামি সাগর রুনির মাসেও দরা পরেনা আর সনের সব ডকুমেন্টস পায় বুবু তুনুর বিচার নাইরে নাইরে বিচার ফেলানির নাই বিচার তৌকির হত্যার সেনা বাহিনি হলো খুন বিচার চলে এখনো আর কি বলবো বলে সেষ করার মতো নয়,0,politics
বঙ্গবন্ধু বঙ্গমাতা সেকচি হাচিনার স্বপ্ন বাস্তবায়িত করুন।,0,politics
মায়ার ভাই ❤❤💐💐🌹🌹 ?,0,politics
এই জাফরুল্লাহ চোরটাও মিডিয়া কাভারেজ পায়!!!!????,0,politics
কানা৷ কাওয়া,0,politics
সরকার যত রাস্তার কাজ করুক মানুষের অভিসাব সরকার কে পতন করবে অভিসাব আসলে খমতা কনো কাজে আসবে না আপনি খমতা থাকেন অনুরুদ করবো মানুষের জান মালের নিরাপত্তা দেন,0,politics
হাসিনা সৈরাচার,0,politics
সরকার দেশ সামলাতে পারছেনা,0,politics
সভাপতির পরিবর্তনের সম্ভাবনা ও নেই এ কেমন গনতন্ত্র?,0,politics
হাতপাখায় ভোট গ্রহণ,0,politics
স্যার কে এখন মারা দরকার,0,politics
মানুষ সম্প্রদায়ের মধ্যে সাম্প্রদায়িকতা থাকবে ।কিন্তু আওয়ামী লীগ হল হিংস্র প্রাণীর কোন সম্প্রদায় না সাম্প্রদায়িকতাথাকতে পারে না ।,0,politics
জাতীয় বিশ্ববিদ্যালয়ের একজন ভিপির নিরাপত্তা ও দেখা যায় না ।,0,politics
কাউয়া কা কা,0,politics
দিদির পুরো কথা শুন্তে দেয়নি সময় সংবাদ এটা এক তরপা বিতরকো হয়েছে।,0,politics
তুই সালা একটা পাগল রাজনীতি নিয়ে তুই ভাবার দরকার নাই তোর থেকে আরো ভালো মানুষ আছে রাজনীতি নিয়ে ভাবার,0,politics
আপনার বক্তব্যে তীব্র আওয়ামী বিরোধীতার প্রকাশ পেল !,0,politics
ভাই সবাই এই ভিডিও টা ডাউনলড করে রেখে দিন । কাল হয়তো এই ভিডিও টা গুম হতে পারে্‌ !,0,politics
রাজাকারের দল বিএনপি,0,politics
সাধারণ সম্পাদক পরিবর্তন করলে দেশের জন্য বর্তমানের থেকেও বেশী ভয় রয়েছে,0,politics
এই ঘরি গূলো বিএম পি জামাত পরিয়ে ছে এবং হাত আছে,0,politics
এটার বিচার চাই 👊👊👊,0,politics
সমায় আসতে আছে ইনুই করবে যা করার,0,politics
আওয়ামী লীগদের পিতা জনাব শেখ মুজিব নিজেই বলেছিলেন সবাই পায় সোনার খনি আর তাঁর দল আওয়ামী লীগে সব চরের খনি,0,politics
নুরুর মত সবাই গর্জি উঠো।,0,politics
কাদের সাহেব এখন বলবে নকল মাল,0,politics
আপনি যেই মডেলের ঘড়ির কথা বলেছেন সত্যি কি উনার ঘড়ি গুলো ঐ মডেলের বা অতটা দামি। আজকাল অরিজিনালের এরুপ রিপ্লেকা হয় যে দুটো পাশা পাশি রাখলে ও বুঝা যায় না। সেখানে ফেসবুকে ছবি দেখে আপনাদের এরুপ সমালোচনা কত যুক্তিযুক্ত সেই প্রশ্ন আপনার কাছে রইল?,0,politics
সব শালা চোরের বাল যার যেটা হাক সেটা সে পায় না যার ক্ষমতা আছে সে পায়,0,politics
আপনাকে ভালো লাগে যুক্তি দিয়ে গরীব বাংগালির সরকারের কুকর্ম ধরে দেয়ার জন্য আসলে সরকার বিপক্ষে কোন স্টেইটমেন্টে মানেই আপনি বিএনপি আর জামাত আশা রাখছি বাংলাদেশের সাথে ভারতে যে চুক্তি হয়েছে সেই বিষয়ে কিছু বলার যে চুক্তি গুলো সংসদ বা জনগন থেকে আড়াল রেখেছে আওয়ামীলীগ ধন্যবাদ ভাই ভালো থাকবেন,0,politics
ওনি ট্রিলিয়ন ডলারের পলিটিক্স বিজনেস ম্যাগনেট!,0,politics
ভাই তুমি এই ধরনের ভিডিও দিও না কারন আমরা তোমাকে হারাতে চাইনা,0,politics
কয়লা শত ধুইলেও ময়লা যায়না কারন আওয়ামী লীগের বড় বড় নেতা এক একটা ময়লার স্তুপে পরিনত হয়ে গেছে।,0,politics
আওয়ামী লীগের নেতা নেত্রীরা কি ইদানীং মাল টাল ইয়াবা গাজা মদ ডেন্ডি কিংবা ফেন্সি খাওয়া শুরু করেছে নাকি🤔🤔😥😥,0,politics
খুনি সন্ত্রাসীদের ধরে না কেন।,0,politics
আওয়ামীলীগের মিথ্যা চাপা বাজি ।আওয়ামীলীগের মধ্যে গনতন্ত্রের রেস মাত্র নাই ।যত চোর বাটপার সংসদে আছে ।সুষ্ঠু নির্বাচন হলে চোর বাটপার সংসদে আসবে না ।সুষ্ঠু নির্বাচন হলে জনগন যাচাই করতে পারে কে কত টুকুও যোগ্য।,0,politics
খালেদা জিয়ার সাথে কারউর তুলনা করা য়ায় না খালেদা জিয়ার তুলনস সে নিজেই,0,politics
ভাই তুমি চালিয়ে যাও,0,politics
ভাই আমি আপনার অনেক বড় ফ্যান,0,politics
তুই চামুচ,0,politics
তিন বারে কয় বছর হয়,0,politics
আওয়ামী লীগের এই ধরনের কাজ কমের কারনে সাধারন মানুষ তাদের প্রতি গৃনা করে।তাই মানুষ ভোট দিতে যায় না।নোমরা রাজনিতি ছি ছি ছি।,0,politics
? 😂😂😂 এখনে ক্লিক করে আবালটারে দেখেন আরেকবার।,0,politics
ভালোবাসা রইলো প্রিয় ভাইটির জন্য অসাধারণ হয়েছে,0,politics
বি এন পি জারা করে তাদের কুনু লজ্জা নাই,0,politics
সবাইর কমেন্টস পড়ে আমি আর কিছু ভলাম না আমি এক মত গালিগালাজ এর পক্ষে,0,politics
তোর মত রাজাকার আওয়ামীলীগে জায়গা হবে আর কোথাও না,0,politics
তখনই নিজেদের কাছে সবচেয়ে বেশি লজ্জাবোধ মনে হয় যখন অন্তত দেশের সবচেয়ে ভোটচুরির চ্যাম্পিয়ন আমু লীগের কাছে অন্যের ভোট চুরির কথা শুনতে পাই আমাদের বয়সে এইরকম ভোটারবিহীন নির্বাচন জীবনেও দেখিনি আমলিক যাই বল সবই হাস্যকর,0,politics
উন্নয়ন হয়েছে তাই তো কোটি টাকার ঘড়ি,0,politics
অধ্যাপক অপু উকিল একজন অশিক্ষিত,0,politics
আর কয়দিন বয়স তো অনেক হয়েছে কাদের সাব কিছুই নিয়ে যাইতে পারবা না দুনিয়া থেকে আপনি যেখান থেকে ফিরে এসেছেন আপনাকে আল্লাহ হেদায়েত করুক,0,politics
পরিবর্তন না হওয়ার সম্ভাবনা সবচেয়ে বেশি তারপরও যদি হয়ে থাকে তবে হানিফ হবে নিশ্চিত থাকেন।,0,politics
একটু মিষ্টি কথা বললেই সবাই হাসে না।,0,politics
কপালে হোডা আলীর গালে জুতা মার,0,politics
শেষ পো দানি দিলাম ডাই বার আর মালিক কে আর সুজোক নাও পাইতে পারি,0,politics
আওয়ামী লীগের একনায়কতন্ত্র নিয়ে হয়তো অনেকেই অনেক কমেন্ট করেছেন এবং করবেন কিন্তু আওয়ামী লীগকে যাই বলেন না কেন কাজী জাফর উল্লাহ সাহেব কে নিয়ে কেউ কিছু কিছু বলবেন না আশা করি। কারণ তিনি এইবার ভোট ডাকাতি কিংবা আওয়ামী লীগের কোনো অপকর্মের সাথে জড়িত নয় আমি যতোটুকু জানি। বরং তিনি আওয়ামী লীগ নেতাদের খেলার জিনিস হয়ে গেছে। বি দ্র কাজী জাফরউল্লাহ ফরিদপুরের আসন ভাঙ্গা সদরপুর চরভদ্রাসন এর প্রার্থী ছিলেন।,0,politics
বাংলার বাঘিনী রুমিন ফারহানা আপু আপনি চালিয়ে যান আমরা আপনার পাশে আছি খালেদা জিয়া আমাদের মা,0,politics
খারাব কিছু বলেনাই,0,politics
এত কষ্ট মেনে নেয়া যায় না সেই ছিল,0,politics
শাহেদ ভাই কাদের সব কিছুর ভাগ পায় এই সময়ে সবচেয়ে বেশী টাকা কামানো আওয়ামী নেতা,0,politics
ওবায়দুল কাদেরকে মানুষ স্যার বলিতেছে হেতা তুই করে কথা বলিতেছে হেতা শিক্ষিত না অশিক্ষিত।,0,politics
শেখ হাসিনা তাদের কে পতেক রাত সময় দে তার কারনে কোউতা লিগ বলে তাদের কে,0,politics
ভাই আমি আমাদের গর্ভ কারণ আপনি সত্য কথা বলেন এই মিথ্যাচারি সরকার সকল সত্যবাদীদের হত্যা করছে নুরুের মত লোকেদের প্রকাশের মারধর করছে,0,politics
জীবনে ও মন্ত্রি হতে পারতা না আওয়ামীলীগ ছাড়া শুকরিয়া কর আল্লাহ র কাছে।,0,politics
কথা সত্য,0,politics
তোমার ভিডিও দেখার অপেক্ষায় থাকি সবসময়,0,politics
হিরো আলম হাসিনার চাইতে ও ভাল,0,politics
জেএম জেএম সর ওভাই ডোল,0,politics
ভাই কী কইলেন আলুর দোষ ঢাকতে থুক্কু আলুর চাষ দেখতে বিদেশে যাইতাছে জন,0,politics
কই ফারহানা আর কই অপু,0,politics
আওয়ামীলীগ মানে ফেরাউনের বংশধর সেখানে কাউয়া কাদের প্রশ্নই ওঠে না,0,politics
নোবেলবিজয়ী আওয়ামী লীগের ভোট চুরির জন্য যা দুটি নিবার্চন প্রমান।,0,politics
মজিব সাহেব এর মেয়ে ছাডা এত বড বড গুম খুন মিথ্যা বলা এবং নাটক কেউ পারবে না উনাকে খুব প্রয়োজন,0,politics
বিএনপি যদি কোন দিন খমতাই আসে তাহলে কি যে হবে,0,politics
রমিন তুই একটা,0,politics
আল্লাহ তুমি মজলুমদের সাহায্য কর,0,politics
ওবায়দুল কাদের একজন ভাল মানুষ আমি মনে করি তার দোষ থাকলে তার শুধু ঘড়ির দোষ আছে,0,politics
এর কারনে যদি আপনার পারসোনাল লাইফে কিছু হয় ভাই? 😥😥😥😥😥,0,politics
প্রধানমন্ত্রী হলেই মানুষের জনপ্রিয় হওয়া যায়না গো সুন্দরী খালেদার চাকরানি।,0,politics
কাওয়া মন্ত্রি,0,politics
আমি সাধারন নাগরিক হিসেবে একটা কথা বলতে চাই । যদি দেশের এবং দলের সন্মান রক্ষার্থে যদি দেশ পরিচালনার সকল পদে পরিবর্তন আসতে পারে যুগের পর যুগ সভাপতির পদ পিবর্বতন হয় না কেন?,0,politics
যদি ভিপি নুরের কিছু হয় দেশে মন্ত্রীর আবাল গিরি ছুটাবে পাবলিক।,0,politics
বাঙালি সংস্কৃতির উপর একটা পর্ব চাই কোনটা বাঙালি সংস্কৃতি বা ঐতিহ্য কোনটা হিন্দু সংস্কৃতি আর কোনটা মুসলিম সংস্কৃতি বিশেষ করে পহেলা বৈশাখের মঙ্গল শোভাযাত্রা ও পান্তা ইলিশ এর উপর বিস্তারিত দলিল সহ সবসময় যেমনটি আপনি দেন☺ একটা বিশ্লেষণ ধর্মী জাতীয় সংগীত পর্বের মত পর্ব উপহার দিলে অনেক উপকৃত হতাম পাশাপাশি সবারই একটা স্পষ্ট ধারনা সৃষ্টি হবে।,0,politics
নুরুও বাড়াবাড়ি করছে ছাত্রলীগও বাড়াবাড়ি করছে এগুলো থামাও সবাই নায়ক হতে চাচ্ছে মিডিয়ার সামনে,0,politics
আল্লাহ গজব পডবে হাচিনা উপর,0,politics
ফাডা কেষ্ট,0,politics
লজ্জার ব্যাপার আমাদের দেশকে এরা পরিচালনা করছে,0,politics
ভাই ধন্যবাদ আপনাকে আপনার ভিডিও দেখে অনেক কিছু যানতে পারি।,0,politics
ইনু সাহেবরা সব সময় ধান্ধার তালে থাকে।,0,politics
অসাধারণ হইছে ভাইয়া । ধন্যবাদ।,0,politics
আল্লাহ আর কতো চুপ করে বসে থাকবেন হয় এই কুত্তাদের বিচার করুন আর না হয় কেয়ামত করে পেলেন,0,politics
হুর ভাই এডি গুলিস্থান থেকে ক্লোন মাল টাকা দিয়ে কেনা। আপনি হুদাই একজন সম্মানীয় ব্যক্তিকে এভাবে অপদস্থ করতে পারে না।,0,politics
চাদা বাজির সুটিং চলতে ছে,0,politics
সত্য ও সাহসী,0,politics
চোদাই এর টাকা থাকলে এক কোটি কেন দশ কোটি টাকা দামের ঘড়ি পড়া যায়,0,politics
উপু উকিলের ডাঃ দেয়কাতে হবে,0,politics
হাইরে টাকা।।। এক লক্ষ টাকার জন্য বেবসা করতে পারিনা।।দিন রাত কাজ করি কিন্তু টাকা চখে দেখিনা।।। অার কিছু মানুষ নষ্ট করে টাকা নষ্ট করে যুবকের ভবিষ্যৎ,0,politics
শেষ পর্যন্ত স্যার ও মিথ্যা বলছে ফোন দেওয়ার পর ও বলছে ফোন দেই নি,0,politics
আভাল বি এন পির দল কি বলতেছে বুঝে নে তারপর কথা বলিস রুমিন ফারহানা মিথ্যা বানিয়ে বলে ওর কাছে সময় আছে রাজনীতি করার ওর সারাদিন চলে যায় মুখে পাউডার মাখতে মাখতে বি এন পি বিএনপি করছ সারাজীবন হাসিনার পায়ে পরে থাকলেও বাংলাদেশের মানুষ হাসিনার ঋন সুদ করতে পারবে না ??? আমরা ভুলে যাই বাংলাদেশ মানেই শেখ মুজিব শেখ হাসিনা তারাই জীবন দিয়ে দেশকে বাঁচিয়ে রাখছে 👨‍🎤👨‍🎤👨‍🚀👨‍🚀,0,politics
কাদেরে একটা মানুষ আর গামছা একটা কাপড় হায়রে বাংলাদেশে,0,politics
ভাই আপনি হিন্দু দল ইস্কন কে এত ভালবাসেন কেন,0,politics
যার টাকা আছে সে তার মনের খায়েস পূরণ করবে এটা খুবই স্বাভাবিক একটি বিষয়। এটি শুধু বাংলাদেশ না গোটা দুনিয়ায় চলে আসছে। এই সামান্য বিষয় নিয়ে আপনি যেভাবে ঢাক ঢোল পিটিয়ে বলছেন তাতে করে আমার মতে আপনার হাতে হাজার টাকার ঘড়ি থাকা উচিৎ না। ওবায়দুল কাদের এর বউ এর আয় খুঁজে বের করেন। তাহলে বুঝবেন কেন উনি এত দামি ঘড়ি পরেন। আমি আগেও বলেছি আপনি নতুন করে বেড়ে ওঠা নতুন চুল্কানি ওয়ালা লোক। আপনার এই মিষ্টি কথায় আমার মত লোকেরা মাথা গরম করা লোক না। তবে আপনার যে আওয়ামিলীগে চুলকানি আছে সেটা অন্তত বোঝায় যায়। বেশি বকা খারাপ। কথাটি মনে রাখবেন।।ধন্যবাদ,0,politics
ভাইয়া কাকড়ার গর্ত থেকে বলছি !!!,0,politics
বাংলার দ্বিতীয় ঈরশাদরে পিডাও ভাইয়েরা,0,politics
ইয়েস আপু অনেকে ধন্যবাদ বি এন পির জয় হবে বি এন পির সাথে বাংলাদেশ মাটিতে দাঁড়িয়ে বিচার করা হবে ইনশাআল্লাহ,0,politics
আবার কম্বলের ফসম উপড়ে দিতে দিতে কম্বল ই শেষ হয়ে না যায়,0,politics
সাধারণ সম্পাদক হবে হানিফ সাহেব,0,politics
সৈয়দ আশরাফ আগে রাজার পুত্র রাজনীতি করে ফকির হতো। এখন ফকিন্নির পুত্র রাজনীতি করে চুরি করার জন্য কেউ করে খমতা চুরি কেউ করে টাকা চুরি।,0,politics
ভোয়াল মাছ ধইরেন না তা হলে সমস্যা।,0,politics
সাহেদ ভাই💚💚💚💚💚স্যালুট😎😎,0,politics
আমার ভাই আবার লাই‌নে আস‌ছে অ‌ভিনন্দন ভাই। মাঝখা‌নে খামোখা ইস্কনের পক্ষ নি‌য়ে কালার হই‌লেন। দেন ভাই আপনার সেই চির‌চেনা স্বভাবসুলভ ভ‌ঙ্গি‌তে বুক চি‌তি‌য়ে সব মু‌খোশধারী ভদ্দর‌লোক‌দের মু‌খোশ খু‌লে দেন ভাই। নাঙা ক‌রে দেন ভাই শালা‌দের।,0,politics
কার সাথে কার তুলনা কাউয়া কাদের কে মানুষ কখন থেকে ছিনলো যখন সাধারণ মানুষের ভোটের অধিকার কেড়ে নিয়ে স্বেচ্ছা চারি সরকার গঠন করলো তা হতে।,0,politics
হিরো আলমের জুতার সমান হয়নাই ওবায়দুল কাদের কে কে আমার কথার সাথে একমত লাইক কমেন্ট করেন।,0,politics
ছাত্রলীগের কলঙ্ক,0,politics
জনগণের টাকা দিয়ে কিনছে কোটি দিয়ে কিনলে কি হইছে,0,politics
ভাল্লাগচে ভাইয়া,0,politics
কি হবে রে,0,politics
মোনাফেক কাজ ষড়যন্ত্র ব্যাক্তিস্বারথ দিয়ে রাজনীতি করা যায় না। বি এন পি’র প্রতিষ্ঠা হয়ে ছিল ষঢ়যন্ত্রের মধ্য দিয়ে। মোনাফেক জিয়া যেমন বিলীন হয়েছে তেমনি তিনার বিবি মূরখ খালেদা ও লম্পট ও দুস্কৃতিকারি পোলা তারেক জিয়াও বিলীন হবে । কারন রাজনীতিতে ষঢ়যন্ত্র কোন দিন তামাদি স্থায়ী হয় না। অন্তত ইতিহাস তাই স্বাক্ষী দেয়।,0,politics
এদের সবার উপর আল্লাহ গজব পরক,0,politics
কিসের মধ্যে কি পান্তা ভাতে ঘি 😂😂😂,0,politics
আগে মনে করতাম ঢাকা বিশ্ববিদ্যালয় পড়া একটা সম্মানের বিষয় কিন্তু এখন মনে হয় ঢাকা বিশ্ববিদ্যালয়ে না পরে ভালো আসি।এখন তো মনে হয় প্রাইভেট বিশ্ববিদ্যালয় নিরাপদ আসি ।ঢাকা বিশ্ববিদ্যালয়ের শিক্ষকদের অনেক সম্মান করতাম কিন্তু ইদানীগ যা দেখি তাতে তারা সম্মান পাওয়ার যোগ্য না ।কারণ পদে পদে মিথ্যা বলে।,0,politics
হায়রে বাংলাদেশ।,0,politics
তুমি বাংাল দেশের সবচেয়ে সাহসি ইউটুবার👍👍👍,0,politics
রেনডির সাথে কখনো টকসতেু যাওয়া ঠিক না এরজরমের ঠিক নাই এর কথা ঠিক থাকবে কোথা থেকে,0,politics
আসা করছি সঠিক লাইনে আসবে।,0,politics
চোরের মার বড় গলা 😂😆😆😄,0,politics
ভাই খুব টেনশনে আছি জে আপনারা কোন ক্ষতি হয় কিনা। আপনার প্রতি দোয়া রইল।,0,politics
ভাইয়া তোমার ভিডিও দেখে আবরারের কথা মনে পরে গেল💔💔💔,0,politics
ওর ভিডিও দেখলে তাহসিন চুতিয়ার কথা মনে পরে মন চায় প্রধানমন্ত্রী হইতে কিন্ত কিভাবে সম্ভব।,0,politics
খালেদা এমন বালের নেত্রী যে ফেনীর জন্য কিছুই করল না,0,politics
আসল কথা কাউয়া রিজেক্ট যা কামাই করছে তাতে বছর তার চোদ্দ গোস্টি বইসা খাবে,0,politics
তারে এখন মন্ত্রী বানাও সব কিচ্ছা শেষ হয়ে যাবে মন্ত্রিত্ব হারিয়ে এখন ঐক্য বাঁচার জন্য শেখ হাসিনাকে ইঙ্গিত দিতেছে,0,politics
মননীয় প্রধানমন্ত্রীর অবশ্যই একটু টনক নড়া উচিত । তা নাহলে বঙ্গবন্ধুর হাতে গড়া দলের এমন কলঙ্ক মেনে নেওয়া সত্যিই অবাক করে ।,0,politics
ভাইয়া আপনি সরকারি জব এ বয়স বিষয় কিসু বলবেন।,0,politics
আল্লাহ আমিন 😳😱😱,0,politics
শিক্ষক হিসেবে এটা মেনে নেওয়া যাই না,0,politics
এক বছরে টি বিমান গেল,0,politics
বড় পরিবর্তন মানে। বিচার মানি তাল গাছ আমার। শেখ হাসিনার সভাপতির পদ বহাল আজীবনের জন্য। এটা নামে গণতন্ত্র। সব পদে পরিবর্তন হওয়া জরুরি। গণতন্ত্রের আড়ালে রাজতন্ত্র চলছে। যা মানুষের সঙ্গে ধোকা বাজি ছাড়া কিছুই না।,0,politics
এমন সত্য তুলে ধরার জন্য সত্যিই মন থেকে ধন্যবাদ,0,politics
তোমার যদি লজ্জা সরম নাই থাকে তাহলে তুমি যা খুশি তাই করতে পার।,0,politics
বাংলাদেশের মাটিতে আওয়ামী নাম নিলে আজু থাকে না পুলিশের সেনাবাহিনী রেফ বিজিপি গজব দে,0,politics
স্যার হলো হাসিনার দালাল এতে কি আপনারা বুজেন না কেনো,0,politics
কার সাথে কি তুলনা দেয় কোথায় বেগম জিয়া আর ওবায়দুর কাদের কাদেরকে কয়জনে চিনে,0,politics
লক্ষ কোটি টাকার হিসেব নেই ভাইয়া এক কোটি টাকার ঘড়ি দেখে কি হবে,0,politics
ভাই এগুলা ক্যাসিনো ব্যবসার শেয়ারের টাকা,0,politics
এই সব চোরের দলকে না বলুন।,0,politics
কপাল এই পাগল গুলা কে পায় কয় কি,0,politics
সালা চোরা,0,politics
কাওয়া কা কা কা অনেক বড় বাটপার😂😂😂,0,politics
এক রার আসতে দে,0,politics
ইনু ইনু ইনু তোর মত ইনুকে আ লীগ আর চায়না বিএনপি আসলে তোর খবর আছে।,0,politics
নুর ভাই আপনার জন্য ভিপি বা রাজনিতি আসে নাই আপনার মারামির সাহজ নাই আপনাকে কেউ ভয় পায় না,0,politics
রুমিন আমার কাছে একটা গল্প আছে আরো ভাল করে বলতে পারবে ।,0,politics
কিছুদিন আগেও তারে সিংগাপুরের হাসপাতাল থেকে অচল অবস্থায় আনা হয়েছে। আল্লাহ ওদেরকে হেদায়াত দাও। 😔,0,politics
অপুউকিল সে একটা মিথ্যা বাদী বেয়াদব এবং যা মনে চাই তাই বলে পাগল একটা।,0,politics
তার মানে কি আরও ক্ষমতায় থাকার আশা?? মরার পরে কি হবে রে মনু ।,0,politics
কাওয়াকে তুলনা করে বেগম জিয়ার সঙ্গে হায়রে বাঙালি,0,politics
সভাপতি কে আগে বাদ দেয়া হক,0,politics
দীদী।আপনি।কি।বলেন।মানুষ।সব।জানে।এমন।কি,0,politics
চোরের নাম খালেদা।,0,politics
সব চুরির সর্বোচ্চ অবসান ঘটিয়েছে এই স্বৈরাচার সরকার,0,politics
তামাশা রে তামাশা,0,politics
অবৈধ বিনাভোটের সন্রাসী কাউয়া কাদিরাকে গনদৌলাই দিন।,0,politics
এরোম চুর আর দেখিন খালেদার মতো।,0,politics
নিজের দলকে কাউয়ার দল বলেছে সেটার ফুটেজ দেখানো দরকার ছিল ।,0,politics
খালেদায় খমতায় থাকা কালিন যদি সৎ থাকত তাহলে জিয়ার মূত্যুর পড়ে এক সাক্ষাতকারে খালেদায় দিখেয়িছিল শুধু জিয়ার পরানো কাপর ছারা আর কিছু রেখে যায়নি তা হলে এখনপ্রশ্ন হল কি ভাবে আজ জিয়ার পরিবার সদস্যগন লন্ডন বসে রাজার হালে চলছে তবে কি বলবেন আলাউদ্দিন এর চেরাগ পাইছে জিয়া পারিবার দলিয়ভাব মাথায় থাকলে তা পাথায় ডুকবেনা বাস্তব নিয়া ভাব্লে পরিস্কার বুযা যাবে,0,politics
ভাইয়া আপনার কথা গোলো কুব মিস্টি এক কথা অসাধান,0,politics
হায়রে কপাল বীর পুরুষ 🧐,0,politics
চোরের মার বড় গলা বিএনপি দেশটাকেই চুরি করে বিক্রি করতে চেয়ে ছিল কিন্তু তা পারে নাই বলেই বিএনপির গায়ে জালা ধরে কোন ভাল কাজ দেখলেই জয় বাংলা জয় বঙ্গবন্ধু জয় শেখ হাসিনা,0,politics
ধন্যবাদ রুমিন আপু আপনাকে,0,politics
আমরা গনতান্ত্রীক দেশ এ বাস করি তো তাই কথা বললে মরতে হবে না হলে হয়রানির শিকার হতে হবে। আসলে গণতন্ত্র এর মানে কি তা বইতে দিয়েন। এটা আবেদন 😖,0,politics
কোথায় রাজ রানী কোথায় বিছানায় মোতনি কাউয়ার সাথে বেগম জিয়ার তুলনা কোন শালায় দেয়,0,politics
আওমিলিগের শোনার ছেলেদের এগুলো কোনো ব্যাপার না না না। ।?,0,politics
শুরু করেছে তারেক কিন্তু এখন করছে জয় এর শেষ কোথায়। আওয়ামীলীগ বলে জয় বাংলা আমি বলি তারেক লন্ডনে জয় আমেরিকায় আর আমরা সাধারণ মানুষ আছি মাইনকা চিপায়।,0,politics
ঘটনা কি???,0,politics
ভাই জনগনের দোষ না এত ঘটনা কোনটা রাইখা কোনটা মনে রাখবে?,0,politics
কত সুন্দর করে খুছিয়ে মিথ্যা বলছে।।। ওকে মনে হয় এইখানে আসার সময় সব কাগজ বানিয়ে দিছে।।,0,politics
কিছু কিছু ছাত্রী ছাত্রদের সমাজের বাইরাস বেয়াদব ছাত্র লীগ,0,politics
লুটের টাকায় কোটি টাকার ঘড়ি কিনে তা আবার দেখায় কতটা নির্লজ্জ ।,0,politics
হিন্দু মহিলা অপু উকিলকে বলছি উনি বলেছে যে বেগম জিয়া নকি ভাঙা ছুটকেছ নিয় আসছে তাই এই হিন্দু মহিলাকে আমি মনেকরিয়ে দিতে চায় যে জিয়াউরহমান ছিল বাংলাদেশের সেনা প্রধান তারপর তিনি হয়েছিলেন প্রধান মন্ত্রি । এখন আমি এই হিন্দু মহিলা অপুকে জিজ্ঞাস করতেচাই জিয়াউরহমানের কী টাকা পয়সা ছিলনা?,0,politics
বাবা মা কত কষ্ট করে মাথার ঘাম পায়ে ফেলে রক্ত পানি করে গ্রাম থেকে ঢাকাতে পাঠায় এই গুলা করতে?পড়াশুনা বাদ দিয়ে কি করছে এগুলা????ঢাকা সিটির ইমেজ টাই এরা নষ্ট করছে এই গ্রামের ক্ষ্যাত গুলা।,0,politics
সোহেল তাজ মত নেতা দরকার,0,politics
সরকার মানুস না আল্লাহ তার বিচার করবেন,0,politics
ওবাদুল কাক্কুকে সাধারন সম্পদক পদ থেকে বহিঃস্কার করা হোক,0,politics
এটাত পাগল মোহিলা তাই এমন কথা বলে আর সেতো কথাই বোলতে পারে না,0,politics
এতো কা কা কইরা কি লাভ হইলো মামু?,0,politics
জনগন বোকা চোদা না কানা ভাই !! আপনার নাটক সবাই বুঝে,0,politics
ওবাইদুল কাদের সাহেব। এক জন ভাল মানুস আমরা ওনাকে চিনি এবং জানি,0,politics
একটি মেয়ে একটি ছেলের সাথে আগুুল তুলে এ ভাবে কথা বলে তাও ছারের সামনে তুমরা পুরুষ নামে ধাউদ,0,politics
অনেক সাহসী একজন ইউটুবার।,0,politics
প্রশাসনে কি করে ? আমার বিশ্বাস এগুলো করায়,0,politics
এগুলো গুজব।,0,politics
সব বাংলাদেশের মানুষের পকেট কেটে নেয়া টাকা। চুরির টাকা। আর উনাকে জিজ্ঞেস করলে উনি বলবেন সব কপি🐸,0,politics
এগুলি তো মৃত্যুর মুখ থেকে চিকিৎসা শেষে সুস্থ হয়ে দেশে ফেরার পর উপহার পেয়েছে! আমি তো গত বছরেও টাকা দামের ঘড়ি পরতে দেখেছি! হুদাই!,0,politics
কেন যে মানুষ মিথ্যা কথা বলে অপু নেই কিন্তু বলে আছে গালি খাইতে ভালো লাগে এজন্য হয়তো বা মিথ্যা কথা বলে,0,politics
শিক্ষিক আওয়ামিলীগের দালাল,0,politics
যারা ভারতের দালালী করে তাদের কি হবে,0,politics
বাংলাদেশের এক মাত্র নেত্রী বেগম খালেদা জিয়া তার কোন তুলনা নেই,0,politics
আমার ক্ষমতা থাকলে সব কয়টারে ধইরা মুখে পলিথিন দিয়া ম্যানহোলের ভিতরে ঢুকায়ে দম বন্ধ করে মেরে ফেলতাম বিশ্ববিদ্যালয়ের পরিবেশ নষ্ট করতাছে সব সালারা😡😡😡,0,politics
বাংলার নায়ক কাদের ভাই,0,politics
ভাই আমার কোন ঘড়ি নেই কাউয়া কাদের কে কি বলবেন মেহেরবানি করে আমাকে একটা ঘড়ি দান করতে😂😂😂,0,politics
নিশ্চই এটা আওয়ামীলীগ এর কোন পাগল নেতা খালেদা জিয়ার সাথে কাউয়া কাদেরের তুলনা করেছে।। কারণ এরা সবাই পাগল কোথায় কি বলা লাগবে এটাও জানে না,0,politics
ভাই ওবায়দুল কাদের সাইকেল এবং পটু টাংওলা লোক না এরা বিটিশ আমলের মালদার পাটি,0,politics
কই যাই সরম পাইছি,0,politics
কি বলব সবই কপাল,0,politics
বেশি সত্য বলেছেন। এ জন্য খুব ভাল লাগেনি। কাদের চাচাকে এই প্রশ্ন করলে হয়তো গুজব বলেই চালিয়ে দেবেন। বাকিটা পাতিহাসের ডিম,0,politics
এই আওয়ামী লীগের বিরুদ্ধে মাননীয় প্রধানমন্ত্রী কাছে বিচার দাবি করি,0,politics
অপু মিথা ভাদি,0,politics
মনুরা তখন ডিম ছোরে মারছো 😋এখন পিয়ার দাও 😃🇧🇩,0,politics
যদি অাগুন জ্বালাতেই চাও ভাইয়েরা তয় নিজেদের বাড়িতে গিয়ে জ্বালাও।দেশের সম্পদ নষ্ট করো না।,0,politics
কিসের সাথে কি? পান্তা ভাতে ঘি।,0,politics
আকাটার বউ কি শেখের জন্মা।,0,politics
ইনু ভয় দিচ্ছে। জংগি তৈরি করে ছেরে দিবে অাবার।এটা সতর্ক বানি।,0,politics
চোরের মার বড় গলা সে কথাটা চোট বেলা থেকেই সুনে আসছি বাস্তবে তাই চোরের মা বড় গলায় কথা বলে এই কারনে ছেলে যদি চুরি না করে তাহলে ভাত জুটবেনা বিলাশিতা করতে পারবেনা তাই অপু উকিলকে বলছি দল করেন ভালয় কথা তবে নেয়ায়কে নেয়ায় বলেন অন্যায়কে পরি হার করুন শিক্ষিত মানুষ হয়ে যদি সু শিক্ষার আলো ছাড়াতে না পারেন তাহলে সারা জীবন টাই অনদয় কারের গুরে কাটাবেন,0,politics
ভাই আমরা জনগণ মনে করি আজকের আর আগের আওয়ামীলীগ এক না বতর্মান আওয়ামীলীগ অত্যন্ত নিকৃষ্ট একটি দলে পরিনত হয়েছে এদের কথা বার্তার দ্বারা প্রমাণীত হয় না,0,politics
হাসি পাই,0,politics
খালেদাজিয়া,0,politics
এই ঘরির দাম কম।,0,politics
আওয়ামীলীগের পতন ঘটবে আওয়ামীলীগের দাঁরায় পতন শুরু হয়ে গেছে এটা শুধু সময়ের ব্যাপার??,0,politics
হুম দেখলাম কাওয়া অপুর দুধু টিপলো,0,politics
পরিবর্তন করে লাভ নেই।যারা বিনাভোটে নির্বাচিত তারা কখনও দেশের কথা ভাবে না,0,politics
মিথ্যাবাদী ও আবার টিচার কেমনে হয়,0,politics
আমার ঘড়ির দাম ইতালির বাংলাদেশেি টাকা হাজার টাকা,0,politics
ভাই সবাধানে থাকবেন এরা কতটুকু খারাপ তা আপনি চিন্তাও করতে পারবেন না!!!,0,politics
শাহেদ আলম তেল বাজি সত্যিই তুমি করছ কাদের কিছু অনুদান দিয়েছে ?,0,politics
সে কি দেয় উকিল কি দেয় তাকে চুচা দেই 🤔🤔🤔,0,politics
জয় কি করে বাংলাদেশ য় ধুনি হয়,0,politics
যুদ্ধাপরাধী মীর কাশিম আলীকে ফাঁসি থেকে বাঁচিয়ে দেবার কথা বলে তার ভাই মীর মাসুম আলীর দেওয়া টাকায় মার্সিডিজ গাড়ি চালান। কাজ তো করেননা কিছু। আমেরিকায় বাসা ভাড়া দেন না নিয়মিত। ইউটিউবে মিথ্যাচার করে কী লাভ?,0,politics
কাজী জাফরউল্লা কে এখনো কেন দলে রাখছে।,0,politics
আমার জন পছন্দের ও প্রিয মন্ত্রী ওবাদুল কাদের।,0,politics
আজকাল প্রকাশের চুরি হতে দেখলে ওকে ওকে কিছু বলা যায় না,0,politics
ইমু একটা আসলে একজন দালাল টাইপের মানুষ এক কথায় বামপন্থী র উপযুক্ত নয়,0,politics
আপনি এই চাকরি ছারবেন আপনাকে,0,politics
ভাই প্রতি টা কথা সুন্দর ভাই আর সব সত্য কথা।,0,politics
কথায় লজিক ছিল ধন্যবাদ ভাই,0,politics
কিচ্ছু হবে না,0,politics
শুনুন আমি নিশ্চিত প্রশাসন এগুলো করায়।,0,politics
বাঘ যদি বুড়াও হয়ে যায় তার পরেও বাঘই থাকে বেগম জিয়া ছিলেন বাংলাদেশের একমাত্র মহিলা প্রধান মন্ত্রী এখন শেখ হাসিনা হচ্ছে বর্তমান প্রধান মন্ত্রী কে ভালো ছিল কে খারাপ তা জনগণের খুব ভালো করে জানা আছে তবে এই দুই প্রধান মন্ত্রীর সাথে কারোর তুলনা হয় না হবে না,0,politics
ইনু সাহেব। নিজের ব্যাক্তিত্ নিজেই নস্ট করছেন। এখন আগামী দিনের জন্যে আল্লাহর কাছে মাফ চান।,0,politics
ঢাকা বিশ্ববিদ্যালয় থেকে ছাত্রলীগকে নিষিদ্ধ করা হোক।,0,politics
অইটা কোন সালির বাচ্চা আদে সালি অভিশাপ লাগবো বাংলাদেশি গো ফারহানা আপনাকে সেলুট,0,politics
হাসিনার পায়ে ধরে মা বল,0,politics
আপনাকে ধন্যবাদ,0,politics
ভাই নুরুল হক নুরুকে নিয়ে একটা ভিডিও দেখতে চাই,0,politics
ধন্যবাদ মহামান্য হাইকোর্ট বেসিক ব্যাংকের কোটি টাকা আত্মসাত করে বহাল তবিয়তে থাকা অমানুষের জামিন বাতিল করায় অভিনন্দন। প্রাইভেট ব্যাংকের কাবুলিওয়ালা মার্কা অত্যাচার চলে শুধুমাত্র স্বল্প লোন গ্রহীতাদের উপর। কোন ব্যাংকের লোন শাখায় যদি যান দেখবেন কিভাবে লোন গ্রহীতাদের সাথে ব্যাংকের শিক্ষিত অফিসারদের মা বাপ দাদাদের কবর তুলে গালিগালাজ করে ????????? এই তো সেদিন ঢাকার মিরপুরে প্রাইভেট ব্যাংকের লোনের সূদের বোঝা আর ব্যাংকের অমানূসীক চাপ সহ্য করতে না পারায় স্বপরিবারে আত্মহত্যার পদ বেচে নিয়ে দুনিয়া থেকে চির বিদায় নিলেন । আল্লাহ্ তাদের জান্নাতূল ফেরদৌসে স্হান দান করুক আল্লাহ্ হূম্মা আমিন। এই কয়দিন আগে অর্থনীতিবিদ ফোরামে উটে আসে বাংলাদেশের প্রাইভেট ব্যাংকগুলোর সুদের হার নাকি পৃথিবীর আর কোন দেশে নাই । এই ব্যাংকগুলো কাবুলিওয়ালাদের মত শহরেই বেপরোয়াভাবে লোন সূদের ব্যবসা চালিয়ে স্বল্প আয়ের মানুষদের নিশ্বেষ করে ব্যাংক মালিকরা আংগূল ফূলে কলাগাছ হচ্ছে । অথচ এদের প্রায় ডাইরেক্টরের পিছনে হাজার হাজার কোটি টাকার ব্যংক লোন আছে সরকারি ব্যাংক গূলোতে। বাংলাদেশের মত দেশ বলে ওলট পালট করে খেতে পারছে। সামান্য লোনের জন্য যদি সাধারন মানুষের জেল জরিমানা হতে পারে তাহলে এই মহা চোরদের শাস্তির আওতায় আসছে না কেন??? এই প্রাইভেট ব্যাংকগুলোর সুদের রমরমা বাণিজ্যে করার সুযোগ করে দিয়েছেন বি এন পির সাবেক অর্থমন্ত্রী সাইফুর রহমান এবং তিনি যত ব্যংক আইন করে গেছেন সব ব্যংকারদের স্বার্থ সংরক্ষণ করা হয়েছে তাহাতে লোন গ্রহীতাদের উপর মরার উপর খাঁড়ার ঘা বাড়িয়ে দিয়েছে ।আমাদের অর্থ মন্ত্রী বড় বড় কথা বলে কিন্তু ব্যাংকগুলোর এই সুদের মারপ্যাঁচে জনগনের দূঃখের কথা তিনি একটিবারও চিন্তা করার সময় নাই তাই আমাদের প্রানপ্রিয় প্রধানমন্ত্রী শেখ হাসিনা কে অনূরোধ ! এই ব্যাংকগুলোকে সুদের হার এ নামাতে বলেন এবং শহরে সুদের কারবার পরিত্যাগ করে গ্রামে শাখা প্রশাখা খুলে কৃষকদের স্বল্প সুদে লোন দিয়ে গ্রামীন অর্থ নীতিকে চাংগা করা এখন সময়ের দাবী ।তাহলেই আপনার নির্বাচনী শ্লোগান গ্রাম হবে শহর পরিকল্পনা সফল হবে।আল্লাহ্ হূম্মা আমিন এবং আলহামদূল্লিহ ।জয় বাংলা জয় বঙ্গবন্ধু ।শোষিতের বিপ্লব দীর্ঘজীবী হউক ।অনূরোধক্রমে মোঃ জসীমউদ্দীন চৌধূরী বাংলা । বাংলা ভবন সাতকানিয়া ।চট্টগ্রাম ।,0,politics
ভাই তুইও দালালি শুরু করলি নাকি?,0,politics
কাদের আবারো সাধারণ সম্পাদক পদে থাকুক। কারণ কাদের অনেক যোগ্যবান ও সত।,0,politics
আমরা আপনার পাশেই আছি। এগিয়ে যান,0,politics
সবই তো বুঝলাম তবে প্রশ্ন একটাই বিড়ালের গলায় ঘন্টা বাঁধবে কে ?!!!,0,politics
এখনো সময় আছে নুরু ভাই পাশে দাঁড়ান নয় সশস্ত্র বাহিনীর হাত থেকে বাঁচবে না। ভালো মানুষ রাখবে না,0,politics
নুর ভাই সত্যের পতে এগিয়ে চল কুতা লিগের বিচার আল্লাহ করবেন ইনশাআল্লাহ,0,politics
ফেবারিট ইউটিবার লাভ ইউ ভাই❤❤❤❤❤,0,politics
খালেদা জিয়া জেলে সেখানে বসে সরোজন্ত করে ইনু পাগর পুলিশ জেলার কারা রখী কিকরে ইনুরে পাবনা নেওয়া উছিত,0,politics
এবং আজাহারি এর টাকা পয়সার পরিমাণের উপর একটা প্রতিবেদন করুন প্লিজ। ধর্ম বেইচা কত কামানো যায় মানুষ জানুক,0,politics
পুলিশরা সব জারোঃ সন্তান দেশটারে ওরাই ডুবাইলো আবার বড়ো বড়ো কথাকয় জুতায় গ্বু লাগাইয়া ওদের মুখে লাগানো উচিঃ,0,politics
ইনু হতাশ। চাটুকারিতা করে লাভ নাই।,0,politics
আওয়ামীলিগ ছারা নির্বাচন করলে ইনু সাহেব কত ভোট পাবেন সে নিজেও জানেন।।,0,politics
এগিয়ে যান,0,politics
আওয়ামী লীগ দলের বাইরে যারা ঐক্য করেছেন তাদের দিন শেষ তাদের সময় এখন ফুরিয়ে গেছে আওয়ামী লীগের কাছে তারা এখন একাই একশ কাউকে দরকার নেই ইমরান এইচ সরকার এর মত অবস্থা হবে বাকি দলগুলোর,0,politics
ওবায়দুল কাদের সাহেবের সাথে খালেদাজিয়ার যারা তুলনা করবে তারা পাগল। খালেদাজিয়া একজন অশিক্ষিত মহিলা কাদের সাহেব ঢাকা বিশ্ববিদ্যালয় পডুয়া। কাদের সাহেব ছাত্র রাজনীতির মাধ্যমে গড়ে উঠা একজন নীতিবান নেতা খালেদাজিয়া উড়ে এসে জুড়ে বসা অযোগ্য ও লূটপাট কারী দলের প্রধানমন্ত্রী।,0,politics
ইনু খান ডায়েরিয়া থেকে মুক্তি পান।ইনু ডায়েরিয়ার একটি বিশ্বস্ত আস্তা,0,politics
সব কয়টা শয়তান,0,politics
ব্যাপারটাতো খুব মজার! ভালো লাগলো 👍👍👍দয়া করে আমাকে করুন,0,politics
আওয়ামী লীগ কিছু লোককে টকশোতে নিয়ে আসে যারা মিথ্যা কথা বলতে একটু ও মুখে বাঝে বর্তমানে জনগণ আওয়ামী লীগকে কতটা ভালোবাসে তা সরকার ভালো ভাবেই বুঝতে পারছে তাই সরকার ভোটের আগের দিনই ভোট কারচুপি করছে কাউয়া কাদের এর সাথে গনতন্ত্রের মা বেগম জিয়ার সাথে তুলনা হাস্যকর ছাড়া কিছু না কথায় আছে চোরের মার বড় গলা,0,politics
ভিউ এতো কম কেন??,0,politics
আমি মনে করি যে কাজ শেখ মুজিব করতে পারে নি সে কাজ টা শেখ হাসিনা করছে আসলে আমি কি বলতে চাইছি একটু ভাবেন,0,politics
তর সাথে মেয়ে কি রাজনৈতিক করে রাতে কি মেয়ে চাএদলরাজনৈতিক,0,politics
বাটপারি র একটা সিমা আছে,0,politics
চোরের বেতন কত? চোর কোটি টাকার ঘড়ি পায় কই?,0,politics
অপু উকিল কিভাবে উকিল হলো বংশধারা থেকে কি মিথ্যাচারের ট্রেনিং পেয়েছে নাকি? এসব অসৎ মানুষগুলোর জন্যই দেশ এত অধপাতের দিকে যাচ্ছে। এরা সত্য মিথ্যা ন্যায় অন্যায়ের পার্থক্যও শিখে নাই। রুমিন ফারহানার মত সম্মানিত নেত্রীকে এরকম একটি বখাটে মেয়ের সাথে দিবেন না। এটি যায় না। পাল্লাতে তুলার সময় মাপ নিবেন কার ওজন কেমন? এসব করে আপনারা বখাটেদেরে মানুষ বানানোর চেষ্টা করছেন। কিন্তু এরা হাজার বছরেও মানুষ হবে না। তবে এটিও ঠিক ওখানে তো বখাটে ছাড়া মানুষ নেই।,0,politics
ডাকাত,0,politics
এটাই ঠিক আছে ট্রাফিক সার্জন সপ ত ঘুষখোর,0,politics
ইনুর ব্যবহার শেষ,0,politics
ভাই গান গুলি জোস হইছে,0,politics
তুই ইনু বাংলাদেশের জন্য একটা বাইরাস।,0,politics
কাউয়ার বাচ্চা,0,politics
কামড়া কামড়ি লাগছে,0,politics
ভাই দিন আগে হলেই ও পদ হারাতো। এখন আর কি হবে।,0,politics
নেএ নিউজ যা দেখাইছে সব ঠিক কিন্তু সব গিফট করা,0,politics
দেশটা কবে ভালো হবে। কষ্ট হয়।,0,politics
পুলিশ যদি মানুষ হতো !!!,0,politics
চোরের চোর কথা মানায় না,0,politics
ওবাইদুলকাদেরতুইমনতিরিনাবনিযানাটককুমপানিতকাজকরারদরকারকেনতুইনাঠকভালজান,0,politics
এর দৃষ্টান্তমুলক ব্যবস্থা নেয়া হোক,0,politics
অনেক চালক হয়েছেন এক জন কে বলার সুযোগ দিয়ে। অন্য জনকে খুব কম সময় দিয়ে যাতে মুল কথায় আসতে না পারে আপনাকে অনেক পাবেন।,0,politics
আমার কেন জানি রাজাকার দের কথা খুব ভালো লাগে,0,politics
যে যার যোগ্য নয় তাকে সে পদ দেওয়া উচিৎ নয়।বোকা শুধু অভিযোগ করে,0,politics
জাহাঙ্গীরনগর বিশ্ববিদ্যালয় হাঁটতে শুরু করেছে। এক মাস দুই মাস তিন মাস ছয় মাস করে বহিষ্কার। জরিমানা । একজন দুইজন নয়। ডজন ডজন । এরা কারা?,0,politics
ইনুকে হাসিনার বাড়ির দারোয়ানের চাকুরী দেওয়া হোক,0,politics
ওবায়দুল কাদের আর হিরো আলমের কোম্পানির লোক হিরো আলমের যোগ্যতা ওবায়দুল কাদের কি যোগ্যতা আছে,0,politics
কথায় আছে চোরের মায়ের বড় গলা আল্লাহ তুমি বিচার করো,0,politics
মাল খাইছে শালায়😄 ডিম কি কাঁচা ছিলো,0,politics
খালেদা জিয়া পায়ের জুতা সমানই সম্মান নাই মিথ্যা বাদী কাদের না,0,politics
সালায় কয় কি কাওয়া রে খালেদাজিয়া সাথে তুলনা করে ছি ছি কাওয়া,0,politics
নিঃর্শতে মুক্তি চাই খালেদা জিয়ার,0,politics
সার যুদি কেও উপহার দিয়া থাকে?,0,politics
? অনুসন্ধান করতে গেলে ইলিয়াসের মত ইউএসএ পালানো লাগবে নাহলে মৃত্যু অনিবার্য। ট্রেন দুর্ঘটনায় মৃতদের যদি হাজার করে দেয়া হয় তাহলে কেটি টাকা দূর্নীতির শাস্তি কাদেরকে বার জনগণের সামনে ফাসি দিতে হবে। খালেদাকে সহ।,0,politics
আমার ঘড়ির দাম টাকা,0,politics
জে হয় মাদবর সে ছাই ছুদবার,0,politics
! মজা পাইলাম।। শেখ হাসিনার পা চাটা গোলাম।।🤔🤔,0,politics
সে হারামির দল আওয়ামী লীগ বিএনপি জনগণের ভোটে ক্ষমতায় এসেছে আওয়ামী লীগ মানেই বিনোদন মিথ্যা বলে বলে দেশটাকে ধ্বংস করে দিয়েছে ওকে যেরকম বলে উন্নয়নের কথা শাওয়ার বাল দেশে কোন কিছু হয়নি ভোট চোরের দল আওয়ামী লীগ,0,politics
এসব ঘড়ি দিয়ে দেখলে কি ভবিষ্যৎ দেখা যায় নাকি সময় ভাল যায় আজ আমার দামি ঘড়ি নাই বলে আমার খারাপ যাচ্ছে,0,politics
ইনুর অবস্থা ইমরানের মত হতে যাচ্ছে বিশ পয়সার থেকে এইমাত্র এক পয়সায় নেমে এসেছে।,0,politics
আমি বুঝতে পারি না এই মানুষ গুল কি মানুষিক ভাবে বিকার গ্রস্থ কিনা ।। এত দামি ঘড়ি ? একটা সাধারন ঘড়ির চেয়ে কি ভাল সময় দিবে ? আর রইলো বিলাস বহুলতার কথা । ওনার যে ইনকাম তার সাথে অবশ্যই এই ঘড়ি ম্যাচ করে না । তাহলে দাড়ায় কি ? উনি হল একটা মহা চোর আজ যদি উনি কোন বড় বাবসাই বা দাউদ ইব্রাহিম এর মতো লোক হত তাও মানা যেত । উনি কোটি টাকা চুরি করলেন সব চুরি তে ই কষ্ট এবং রিস্ক আছে এত কিছু করার পর উনি নিজে ই নিজের কপালে চোরের সাইন বোর্ড লাগালেন ।। এটাকে ই বলে আহাম্মক,0,politics
সভাপতি কেনো রদবদল হবে না,0,politics
শেখ হাসিনা বড় না আন্দালিব রহমান পাথর্??????হা হা,0,politics
এতো দেখি এ চেনেল অলার মা তাইনা।।,0,politics
সিটিং,0,politics
এই ঘড়ি গুলো অবশ্যই বি এন পি জামায়াত তাকে জোর করে পরিয়েছে। মুক্তিযুদ্ধের চেতনা নেই বলেই তারা কেসিনো বেবসা না করে একজন কাউয়া র পেছনে লেগেছে।,0,politics
অনি এসে আরো জমজট গুন বেড়ে গেছে হাইরে দেশ এটা নাকি সাদিন দেশ। পাগলামি,0,politics
খালেদা জিয়ার মুত্তি চাই আমরা,0,politics
ভাইয়া বিশ্ব রাজনৈতিক অবস্থা নিয়ে অনেকদিন থেকে আপনার কোন ভিডিও আসছে না।,0,politics
মন্ত্রী সাহেব যদি ট্রাফিক পুলিশের কাজ করতে হয় মাসে মাসে সার্জেন্ট দের বেতন দেয় বাল ফালাইতে,0,politics
অপু কুকিলের মুখে কথা আসছেনা তাড় পর ও মিথ্যাচার করছে হাসি বুবুর মতো।,0,politics
পিতা মাতা খারাপ হলে সন্তান ভাল হয় আবারো পিতামাতার চেয়েও সন্তান যখন খারাপ হয় তখন লজ্জা আর ছি ছি ছাড়া কোন উপায় থাকেনা!,0,politics
নতুন করে পুরান ঘটনা,0,politics
তোরে ভালো করে পিটায় না কে,0,politics
কাউয়াকে বাহির করে দিলে জাতি খুশি হবে,0,politics
শাবাস ভাই সাহশ ও বীধহী বাংলা বাঘ,0,politics
খুবি সতৌকথা!,0,politics
নুরুকে ডিম না মেরে জুতা মারা উচিত ছিলো,0,politics
ওর বাবা নাকি স্কুল মাষ্টার ছিলো কিন্তু ছেলে হলো চোর আর কথা বলে বাটপারের মত,0,politics
যারা টাকা খেয়ে দরবেশ হয়েছে তারা এখন সরে যাবে কারণ সামনে তো নির্বাচন,0,politics
তার এবং তার পরিবারের সব দৈনন্দিন জিনিসের ই আকাশ ছোঁয়া দাম হবে নিঃসন্দেহে।,0,politics
ভাই আপনিও না একটা জিনিষ।,0,politics
রাইট,0,politics
দিল তো দেইনি কাউকে,0,politics
সাহেবের চালকের বেলট পড়ে নাই এটা মিডিয়া দেখে নাই,0,politics
পাগলের মাংস না খেলে আওয়ামী লীগ হওয়া যায় না,0,politics
আর কত গ মাই শেখ হাসিনা ছাএলীগ দিয়া শিক্ষার পরিবেশটা নষ্ট করবা! এবার ওদের থামাও।,0,politics
হায়রে ছাত্র লিগ৷ এদের নিশিধ্ব করা হোন,0,politics
কি দেখাইলেন ভাই ধন্যবাদ ভাই আপনাকে,0,politics
ফারহানা মেডাম আপনিব খালেদাকে দুধ দিয়ে ধুয়ে পানি খান। এতে শেখ হাসিনার একটাও লোম পড়বে না এই গুলি বলে কি লাভ পারলে রাস্তাই আন্দলন গড়ে তুলুন শুধু মুখদিয়ে বগবগ করলে খালেদা জিয়া বাহির হবে না এইটাওআমাথায় রাখতে হবে।।,0,politics
আমাদের বর্তমান নেতাদের মাঝ থেকে কি ভালো কিছু আসতে পারে? না। পরবর্তী জেনারেশন এর জন্য প্রয়োজন রাজনীতি বহির্ভূত কিছু মেধাবী ও সত মানুষের।,0,politics
স্বাধীনতার অভাবে করতে পারেন নাই এইটার জন্য খারাপ লাগচে।,0,politics
কাদের সাহেবকে জনগণ কত ভালোবাসে তা তিনি অসুস্থ থাকা অবস্থায় বুঝা গেছে। প্রতিটি পোষ্টে হাজার হাজার কমেন্ট পড়েছে উনার সুস্থ্যতা কামনা করে। সে সব যদি উনি এখন দেখেন তাহলে আবেগে আবার অসুস্থ হয়ে যেতে পারেন।,0,politics
‌সেলুট ফারহানা অাপু‌কে ।,0,politics
এটা কি সাদিন দেশ আমাদের ভাবতে অবাক লাখছে,0,politics
এদেরকে ফাঁসিতে ঝোলানো হোক,0,politics
শেখ হাসিনা হলো ইসলামী মাইন্ডেড একজন শাসল। ইসলামে গণতন্ত্র হারাম তাই উনি দেশে গণতন্ত্র বাদ দিয়ে একনায়কতন্ত্রে রেখেছেন জয় বাংলা,0,politics
এর আগেও শুনেছিলাম জাতীয় সংসদ নির্বাচনে পদ হারাচ্ছে জন পুরাতন এমপি! বাস্তবে আমরা কি দেখলাম? যে লাউ সে কদু🤣,0,politics
জানোয়ারদের আইনের আওতায় আনা হোক ওদেরকে ফাঁসিতে ঝুলানো হোক,0,politics
এরাই দেশের বড় চোর।,0,politics
ভাই আপনি সাহসী এরকম কথা কেউ বলে না আল্লাহ আপনাকে হেফাজত করুক জাজাকাল্লাহু খাইরান কিন্তু সাউন্ড প্রবলেম বুঝা যায় না ভালো করে,0,politics
কাওউয়ার সাথে তুলনা করা যায়,0,politics
আমার মনে হই বালো কাজ কিনতো বি আর টি চেক করা দরকার,0,politics
আওয়ামী সব গুলো মুর্খ,0,politics
ওবাদুল ভাই ঠিক আছে।,0,politics
এমন দিন আসবে আওয়ামী লীগের নাম বাংলার জমিনে থাকবে না ইনশাআল্লাহ,0,politics
আগে উবায়দুল কাদের কে দল থেকে বহিস্কার করেন পরে তাকে গ্রেফতার করেন সব কিছুই বেরিয়ে আসবে টাকার বিনিময়ে অনেক তেনা কে নেতা বানাই ছেন এই উবায়দুল কাদের,0,politics
শুধু কাদের না আমার মনে হয় অপু উকিলের কাছে ও বেগম জিয়া ছোট মর্যাদায় ?,0,politics
আবরারকে নিয়ে প্রতিবাদী গান শুনুন আমার চ্যানেলে গানের প্রতিটি শব্দই যেন এক একটা অ্যাটাম বুম শুনলেই গা শিউরে উঠবে - - -,0,politics
বিতর্কিত অথবা যাদের নামে রিপোর্ট আছে বর্তমানে যারা আছে যাদের বিএনপি জামাত কানেকশন ছিল তাদেরকে দেখতে চাই না শুধু মুখে বললেই হবে না।।,0,politics
কাওয়া মন্তী ওবাই দোল কাদের,0,politics
কাদের হেতের এলাকায় আসে না ভয়ে,0,politics
ধন্যবাদ এমন একটা ভিডিও উপহার দেওয়ার জন্য এগিয়ে জান,0,politics
অপু উকিল আজেবাজে কথা বলে। তথ্য বিহীন কথা মিথ্যা কথা বলে। তাকে টকশো তে আনাই ঠিক নয়।,0,politics
আওয়ামী লীগ ছাড়া ইনু জিরো,0,politics
রইট দন্যবাদ,0,politics
এইধরণের কর্মকর্তাদের ছাত্রছাত্রীরা মিলে জুতা পেটা কর!!!!,0,politics
কোথায় খালেদা জিয়া কোথায় কাদের আজব গনতন্ত্র দেশ?,0,politics
ছাত্রলীগ ঢাকা বিশ্ববিদ্যালয়কে সন্ত্রাসী ও গুন্ডামির স্বর্গরাজ্যে পরিণত করেছে ।,0,politics
কই আগর তলা আর কই খাটের তলা কই বেগম জিয়া আর কই কাউয়া টাওয়া গোটা জাতির দুশমন আওয়ামিলীগ,0,politics
এইরকম উচু রুচি সম্পন্ন মন্ত্রীকে পেয়ে বাঙালি গর্বিত 🤣🤣🤣,0,politics
হা হা হা আপনি নিজেইতো লোকজন নিয়ে রাস্তা পুরো জ্যাম করে রেখেছেন। মানুষকে আর কতো বিনোদন দিবেন এইসব লোকদেখানো দায়িত্ব বাদদেন।,0,politics
ভাই অনেক ভালো একটা কথা বলচেন,0,politics
বাংলাদেশের মানুষ বেলা ঠিকমত খেতে পান না এই তথ্য আপনি কোথায় পেলেন????,0,politics
সাবেক অর্থ মন্তী আবুল মাল মুহিত কতো দামের পানজাবী পরতেন শুনেছি তার ও নাকি অনেক দাম ছিলো কতো ছিলো তা জানাবেন কি।,0,politics
আওয়ামী লীগ কি চায়,0,politics
এই বাংলাদেশ আর বাংলাদেশ নেই,0,politics
ওবায়দুল কাদের বরো না খালেদাজিয়া বরো সেটা দেখা জাবে জদি কেনো দিন বিনপি খমতায় আসে তখন সুদু কাদের না পুরা অওমিলিগ ও খালেদার একটা জোতার জখৌ ওনা,0,politics
এই পরিমাণ টাকা দিয়ে বাংলাদেশের একটা জেলার মানুষের সারাজীবনের কর্মসংস্থান করা যাবে,0,politics
যত যাই হোক।তাই বলে একজন প্রধানমন্ত্রীর সাথে একজন নরমাল এম্পির তুলনা হতে পারেনা সে যেই হোক।হাসিনার সাথেও বিএনপির কোনো এম্পির তুলনা হয়না তেমনি খালেদার সাথেও আওয়ামীলীগ এর কারো তুলনা হয়না।এগুলা জাস্ট বোকামি। আর একটা কথা বিএনপি এ একক নির্বাচন দিয়ে টিকতে পারেনি কারণ তখন পুলিশ এত স্ট্রং ছিলনা আর দেশে গণতন্ত্র কিছুটা ছিল।আর এখন পুলিশ র‍্যাবের অত্যাচারে আওয়ামীলীগ দুইবার টিকে গেছে।কিন্তু পুলিশ র‍্যাব না থাকলে আওয়ামীলীগ ও আবার পুননির্বাচন দিতে বাধ্য থাকতো।,0,politics
এদেরকে বছরে দিন মারামারি হয়। এটা বিশ্ববিদ্যালয় তো না ছাত্রলীগের ঘাটি,0,politics
উবায়দুল কাদেরের ছাত্র জিবন শেষ হতে যে সময় লাগছে ঠিক ততখানি সময়ে খালেদা জিয়া রিতিমত একজন গৃহিণী ও দুই সন্তানের মা রাজনীতি করতে যে যোগ্যতা লাগে উবায়দুল কাদেরের তা আছে সামির সুবাধে তিন বার প্রধানমন্ত্রী গর্বের কিছু না,0,politics
প্রধানমন্ত্রী পরিবর্তন চাই,0,politics
শিক্ষক কে লাথি মারে কি ভাবে শিক্ষক হচ্ছেন বাবার মত ।,0,politics
ওরে কাদের😂😂🤣,0,politics
আওয়ামী লীগের নতুন সম্পাদক হিসেবে ডঃ আব্দুর রাজ্জাক কে চাই।,0,politics
দনের খবর,0,politics
সাবাস বোন,0,politics
ভাই আমরা এখনও সাধারণ মানুষ অনেক কস্টে আছি অর্থনৈতিক ভাল । বাংলাদেশের মানুষের ভাগ্য কি ফিরবে?,0,politics
চোরের মার বড় গলা,0,politics
আমার হাতে একটা ঘড়ি আছে মূল্য টাহা,0,politics
ডীমলীগ,0,politics
কিসের কাগজ??? 🙄,0,politics
এই বালের খবর গুলো আমরা দেখছি ইন্ডিয়া থেকে ফেক নিউজ গুলো বন্ধ কর,0,politics
এটাতো পাগল মন্ত্রী সকালে এক কথা বলে বিকালে আর এক কথা বলে,0,politics
কাদেরের বিছানার সঈী,0,politics
ঘড়ি গুলোর মালিক তো আমরাই,0,politics
যে ক্ষমতায় থাকবে সে বড়। সুরন্জিত সেন বলেছেন বিরোধী দলের এমপি হওয়ার চেয়ে সরকার দলের কর্মী হওয়া ভালো। তিনি তার অতীত অভিজ্ঞতা থেকে বলেছেন।,0,politics
এখন তো আপনি রাস্তায় নেমে গাড়ি চেক করছেন ! ছাত্র ছাত্রী যখন মারা গেল তখন কি তাদের কাছে যেতে পারতেন না? তাদেরকে শান্তনা দিতে পারতেনা?,0,politics
একটা কমেন্টও যাইনি আওয়ামীলীগের পক্ষে হাস্যকর 😁😁,0,politics
দেশের মানুষের প্রশ্ন কে এই ওবায়দুল কাদের?,0,politics
যেই দেশে বিরোধী দলের মহাসচিব কে রং মারে পুলিশ সেখানে ছাত্রলীগ তো কিছুই না৷,0,politics
সবগুলো জাহেল কে কাকে সালাম দিবে তা যানে না তারা দেশ চালাতেছে,0,politics
আমরা জানি যে এক জন মহিলা যখন ভাত রান্না করে ভাতে টিপে দিলে সব ভাতের খবর পাওয়া যায় ঐ মহিলা কি হিন্দু তো তাই ও ভাতের খবর কি করে জানবে ও তো বুড়ি ঙংগা পানির নিচে থাকে,0,politics
এই রাজনীতি ফাজনীতি না করে পড়ালেখা কর ভাই বোনেরা।।।,0,politics
ছাত্রলীগের সন্ত্রাসীরা মেরে ফেলতে চেয়েছিলো,0,politics
আমার ঘড়ির দাম প্রায় বাইরের দেশের সবার ই শখ থাকতেই পারে সে নিজেই বলেছে ঘড়িটি গিফট পাইছে আর ওবাইদুল কাদেরের পজিশনে আপনি থাকলেও টাকা হলেও মারতেন ওকে?,0,politics
শুনেছি কালা আজিজ মারা গেছে শুটিংয়ের জন্য কালা আজিজের বাকি অংশ ওবায়দুল কাদিরকে দিয়ে শেষ করা যাবে।,0,politics
ভাই সব মিলে তিন চার কোটি টাকার ঘড়ি হতে পারে আওয়ামীলীগের ওয়ার্ড পর্যায়ের নেতাদের কাছে এই টা কোন টাকা না আর কাদের আওয়ামীলীগের সাধারণ সম্পাদক,0,politics
কাউয়া গো ব্যাক,0,politics
ছৈয়দ আশরাফ আমাদের বাংলাদেশ র গব ❤👍,0,politics
হিসাব দিতে হবে আল্লাহর কার্ডগড়ায়,0,politics
জনগনের ঘাম ঝড়ানো টাকায়।🙄,0,politics
ভাই? তোমার সব ভিডিও গুলো অনেক ভালো লাগে সত্যের আলো ছড়িয়ে দাও প্রতিটা ভিডিওতে এগিয়ে যাও সাহসী বাঙালী পাসে ছিলাম আছি থাকবো,0,politics
আসলে ওবায়েদুল কাদের খুবই একজন ভালো মানুষ না হলে তিনি এতদিনে হাজার কোটি টাকার মালিক হতে পারতেন।,0,politics
শেইম!শেইম!শেইম!আর এদিকে দেশের মানুষের নুন আনতে পান্তা ফুরায়,0,politics
সত্য কথার জয় হোক।,0,politics
”অধীকার হরনকারীরা কখনও সন্মানিত হয়না চিরদিন চোর হয়ে তাকতে হবে যার জন্যে চুরি করা হয় সে ও তখন বিশ্বাস করবেনা চোর বলে ডাকবে । কিন্ত মহাবিচারক শেষ বিচারের দিনে ছাড় দিবেননা । অাশা করা যায় কঠিন বিচার হবে যদি দায়মুক্তির ব্যবস্হা না হয় । বাকীআল্লাহ্ জানেন ।” পুলিশ যদি মানুষ হতো !!!,0,politics
কাদের স্যর ভালো মানুষ আর খালেদা চোর এতিমের টাকা মেরেদিয়েছে বি এন পি জারা করে তাদের কুনু লজ্জা নাই,0,politics
স্যার স্যার না বলে ডাইরেক জুতা মারো কারন সেও একটা ডিমলীগের সদস্য।,0,politics
হাছিনার চামচিকে জুতা মারেন।,0,politics
কাউয়ার সাথে মানুষের তুলনা হা হা হা। দেশটা তো পচা শামুক হয়ে গেছে,0,politics
ভাইয়ের ভিডিও কি এখনও রি ইউজ এলাও আছে?,0,politics
আমার সান্তনু ভাই জিন্দাবাদ। মাশাআল্লাহ এরকম সৎসাহসি মানুষ বাংলাদেশে বর্তমানে অনেক কম আছে। আর আওয়ামিলীগ তাদের মুখের কথা ও মনের কথা কখনো এক ছিল না আর এখনতো তা প্রমানিত। যারা শান্তনু ভাইয়ের ভক্ত তারা এখানে লাইক করে জানিয়ে দিবেন|,0,politics
তাহইলেদুইকোটিটাকাএতিমেখায়াজায়,0,politics
আমি এখন কি করব হাসবো নাকি কাঁদবো। বলেন,0,politics
কেন জানি মনে হয় আমার আওয়ামী লীগের সবাই পাগল । মাঝে মাঝে এমন এমন কিছু কথা বলে না হেসে পারি না । 😃😃😄,0,politics
চলচ্চিত্রের সেরা নায়ক খান বাহাদুর ওবায়দুল কাদের উপস্থিত হয়েছে,0,politics
বর্তমান জ্ঞানী লোকজন সবাই সরকারের দালালি করে,0,politics
রাজনীতি তে যদি টাকার খেলা না থাকতো তাহলে সবাই তার স্ব স্ব কর্ম নিয়ে ব্যস্ত থাকতো তা প্রমাণিত হলো।,0,politics
শান্ত নু ভাই আপনার কথা গুলা অনেক গুছাল।ভাল্লাগে ভাই,0,politics
সবার এরকম কাজ করা উচিত মাএ একদিনের জন্য না প্রতিদিন চাই,0,politics
অনেক অনেক ধন্যবাদ আপনার ভাইয়া আপনার সব ভিডিও মাধ্যমে অনেক গুরুত্বপূর্ণ বিষয় অনেক সত্যি ঘটনা জানা যায় আমি সৌদি আরব থেকে আপনার ভিডিও টি দেখলাম 🇧🇩🇸🇦🕋👈👈👈👈👍💐🙋💝💙💚💞💓💜💕🌹❤✌💯 জাজাকাল্লাহ খাইরান শুভকামনা রইল আপনার জন্য আপনার জন্য অনেক অনেক দোয়া ও ভালো বাসা রইল,0,politics
রুমি একটা চাপা বাজ,0,politics
কার সাথে কি পানতা বাতে ঘিই,0,politics
দৈনিক কোটি টাকার চাঁদা যে উনার পকেটে যায় সে নিউজ আমরা কিন্তু জানি,0,politics
ছেলেদের হলে মেয়েরা কি করতে জায় টি এ সি বসে মেয়ে গুলা গাজা টানে আর কোন কাম নাই,0,politics
নীচের ঘটনা গুলুর সম্পের্ক লিখুন শান্তি বাহিনি র শাথে সরকারি বাহিনি আর্মি নেভি এয়ার পুলিশ লরাই এ নিহত আহতঃ শংখ্যা। শান্তি মিশন এ আফ্রিকা –তে নিহত নিহত আহতঃ শংখ্যা জিয়াউর রাহমান এর ক্যু – এর সময় এ নিহত আহতঃ শংখ্যা ক্যু – এর পর কোর্ট মারশাল এ নিহত শংখ্যা ঢাকা বিশ্ববিদ্যালয় এ এর পর বিভিন্ন সময় নিহত আহতঃ শংখ্যা অন্যান্য শিখ্যা প্রতিস্থানে নিহত আহতঃ শংখ্যা নোয়াখালীর লোক নোয়াখালীতে নয় দূরবর্তী স্থানে হরতাল অবরধ এ নিহত আহতঃ শংখ্যা এ সকল ক্ষেত্রে নোয়াখালীর নিহত আহতঃ শংখ্যা কত? শতকরা হার কত? দয়া করে জানাবেন কি?,0,politics
শিগ্রই এই ঘড়িগুলো কাদেরের পুটকির ভিতর দিয়ে যাইবে আসবে।,0,politics
টাকায় বড় বড় ব্রেন্ডের ঘড়ি আমাদের পুরান ঢাকায় অভাব নাই ।,0,politics
আমার টাকার ঘড়ি তাও টা।সালা পুরা কপাল টাকার ঘড়িও টা কিনতে পারি না।বাহ কাউয়া কাকা বাহ ভাতিজার দিকে একটু নেকনজর দাও।,0,politics
ইনু আওয়ামীলীগকে ছাড়া নির্বাচন করলে জামানত ফিরে পাবে না।,0,politics
অপু উকিল মনে হয় মেয়াদ হীন গাজাঁ খেয়ে আলোচনা আসছে উনাকে কাউয়ার সাথে রাত কাঠাতে দেয়ার জন্য জোর দাবি জানাচ্ছি,0,politics
খালেদারজিয়ামুকতীচাই,0,politics
ধন্যবাদ ভাই কথা বলতে না দেওয়া জন্য,0,politics
উনি প্রধানমন্ত্রী হলে খুশি হতাম আমি,0,politics
ওবায়দুল কাদেরের কি যোগ্য আছে দলের সেক্রেটারি হওয়ার হেতে কাউয়ার মতো কা কা করে খালি,0,politics
আওয়ামীলীগ এর সালি ভালো ভাবে তো কথা বলতে পারিস না কথা বলতে গেছোস কেন।,0,politics
এই হযম তুইতো এক নম্বরের রাযাকার।,0,politics
আমিও ওনাকে খুব সম্মান করি। শুনেছি ওনি যখন শুক্রবারে রাস্তা দিয়ে আসেন তখন ট্রাফিক পুলিশরা তাদের নিজের কাজ টিক ভাবে করে,0,politics
ধন্য বাদ ভোন,0,politics
সব কিছু সবার আগে তুলে ধরেন নেয় এর পক্ষে আন্যয় এর বিপক্ষে আসা করি পল্টীবজি করবে না ধন্যবাদ ভাই,0,politics
যুবলীগ চেয়ারম্যান ওমর ফারুক চৌধুরী কে সভাপতির দায়িত্ব দিলে ভালো হবে,0,politics
হাতির সাথে ছাগলের তুলনা। কোথাই খালেদা আর কোথাই কাদের।মিথ্যা কথা বলা বন্ধ করেন।,0,politics
প্রধাণমন্ত্রী কাদের এর বিষয়ে অন্ধ।,0,politics
ডিমের দাম বেড়ে যাবে দেশের জনগণ পুষ্টিহীনতায় ভুগবে আহারে কি হবে?? কি হবে ????,0,politics
আমার মত যারা রাজনৈতিক বিষয় এ মতামত দিতে চান না নিজের মত থাকতে চান তারা লাইক দিয়ে চলে যান ভাই কারন আমাদের ভাবনা আমরা বড় হবো কিছু টাকা নিয়ে বিদেশে চলে যাবো অন্তত দেশের মানুষ আমার হোগাই বাশ দিতে পারবে নাহ 🤔,0,politics
কই রাজ রানি কই চোত মারানি,0,politics
শ ম রেজাউল করিম হবেন সাধারন সম্পাদক হবেন ।,0,politics
ছাত্রত্তে কেন রাজনীতি ?,0,politics
কুকুর লিক পাগল,0,politics
তোদের যদি জনগনে ভোট লাগতো তাহলে খুজে পাওয়াও যাবে না,0,politics
এমন দেশটি কথাও খুজে পাবে নাতো তুমি সকল দেশের রাজা রানি আমার পথো ভুমি,0,politics
অপুউকিল কে আমার কাছে পাঠিয়ে দেয়,0,politics
এগিয়ে যাও রুম,0,politics
আপনি একটা একটা জিনিস রে ভাই।,0,politics
বাংলাদেশের শিক্ষা প্রতিষ্টান এর দিকে তাকাইলে শিক্ষ গ্রহণ করা ত দুরের কতা শুধু ঘৃণা আসে হায়রে বাংলাদেশ আজ কোথায় গিয়ে দারিয়েছে,0,politics
আরে ভাই আপনি তো বাঘের বাচ্ছা💙💗💙 মানুষের পেটে ও বাঘের বাচ্ছা হয় সে টা জানতাম না।। স্যালুট🖐🖐👌✌,0,politics
মার কেবল শুরু।আরোও চমক আছে।আমরা সাধারন মানুষ শুধু খেলা দেখবো।খেলাতো হবেই।,0,politics
ত্রই সব ঘাড়ি চেকের না অনেক বড় যান যট সিষ্টি করে ওনারা ত্রত বড় তারা কেন চেক করতে হবে পুলিশ কি করে অার বড় কথা হলো ভালো অাইন করল্লে ত পারে সবাইয় মানতে হবে,0,politics
আন্ডালীগ? 😂😂,0,politics
আল্লাহ অবিচারের দিন শেষ করো।,0,politics
নুর অনেক ভালো ওর ওপরে হামলা কেন বার বার আওয়া মিলিগের অততাচার আর কতো,0,politics
ছোট বা বড় যে পরিবর্তন ই হোক আমাদের জাতির কোন প্রকার ভাগ্য পরিবর্তন হবে বলে মনে হচ্ছে না ।দেখছিতো গত এগারো বারো বছর ধরেই ।ব্যবসা বাণিজ্য আমাদের লাটে উঠেছে সততার কোন মূল্যেই এদেশে শুধু দৃরণীতি আর রাজনীতির পোয়াবারো ।,0,politics
সৈয়দ আশরাফ সবথেকে ভালো মানুষ এবং সৎ রাজনীতিবিদ ছিলেন তার তুলনা তিনি নিজেই।,0,politics
ভাই হাজার হাজার সালাম নিবেন আপনার মতো একজন ইউটিউবা পেয়ে আমি ধন্য আপনি আমাদের গর্ব সুধু ধন্যবাদ দিলে কম হবে আল্লা আপনার অনেক দিন বাঁচিয়ে রাখুক আমাদের মাঝে কেউ সত্যি কথা বল্লে আমার ভয় করে কবে যানো হারিয়ে ফেলি নিজের খিয়াল রাখবেন ধন্যবাদ,0,politics
জনসমর্তন ছাড়াই অনেক লম্বা লম্বা কথা দীর্ঘদিন যাবৎ বলে যাচ্ছে।,0,politics
ওডা পাগলা এটা কোন বেপার হলো বছর রাজনৌতিক করে একজন মন্ত্রী কোটি ঘড়ি পরতে পারে নোয়াখালী মানুষ তোর মত পকিরনি না,0,politics
ওর বাবার টাকা না এগুলো এগুলো সব জনোগনের টাকা এই টাকার লোভে তারা খমতার লোভ ছাড়ে না।এবার বোঝ।শালা।,0,politics
এই সব ঘড়ি দেখে আমি সিহরিত!! এটা আমাকে বি এন পি জোর করে পরিয়ে দিছে,0,politics
বা লা নেকেট সানি লিওন,0,politics
সাহসী ইউটিউবার👏 ধন্যবাদ ভাই,0,politics
ধরা খাইছে তিই আর কি,0,politics
কাউয়ার কি সৌভাগ্য কচি কচি মাইয়াগো দেখে দেখে সাইজ মিলাচ্ছে,0,politics
প্রতিটা হোটেল আবাসিক হোটেল চেক করো। প্রতিটা প্রতিষ্ঠানের সন্ত্রাষ কে চিন্হিত করে তোমাদের থেকে আলাদা করে দেশ কে বাঁচাও।,0,politics
একটা চোদার দেশে থাকি। রাতে ইন্ডিয়া ইউজ করি আর সকালে ঘুম থেকে উঠে ফেবুকে স্ট্যাটাস দেই ইন্ডিয়ার ঘৃণা করি। আর তাতেই হয়ে যায় আমাদের দেশ প্রেম। এই হচ্ছে আমাদের অবস্থা।,0,politics
সাবাস মানুষের বাচ্চা সিংহ বাঁচতে হয় এক ঘন্টা বাজবে সিংয়ের মত। ♥️♥️♥️♥️,0,politics
ছাএলীগ মানে স্বৈরতান্ত্রিক সন্এাস,0,politics
লীগ মানে চোর লীগ মানে সন্তাসি লীগ মানে নাস্তিক লীগ মানে ভারতে দালাল এদের বয়কট করতে হবে,0,politics
ফালতু লোক,0,politics
কোথায় শেখ স্বাদি আর কোথায় বকরির লাদি,0,politics
দক্ষিণ চট্টগ্রাম প্রায় সব এমপির বৈধতা নিয়ে প্রশ্ন আছে?,0,politics
জুতা পিটা করলা না,0,politics
এই নেতা আজ অসুখ এ পরলে চাদা না তুলে চিকিৎসা করতে পারবে না,0,politics
অবইদ টাকার মালিক এইসব নেতারা,0,politics
সবার আগেই জাফরুল্লাহ বাদ।,0,politics
যুক্তি সম্পূর্ণ কথা বলতে এবং শুনতে সত্যি ভালো লাগে আপনার শুভ কামনা করছি!,0,politics
ধন্যবাদ।অনেক দিন পর এলেন ।,0,politics
জনগণের খমতা চোর ডাকাত খুনি অবৈধ সরকার নমরুদ ফেরাউনের হটাও।,0,politics
কাউয়া 🐓🐓🐓🐓,0,politics
কাদের স্যারের সাথে তুলনা করা যায় একমাত্র হিরো আলমের সাথে এরা খায় বেশি স্বাস্থ বাড়ে না,0,politics
মন থেকে দোয়া রইলো একদিন অনেক ভালো কিছু করবেন,0,politics
ফালু তুমি কোথায়? তারেক তো দেশে নাই তারেকের রাতের বিছানার সঙ্গি এখন একা এই সুযোগে তুমি চান্স নিতে পারো,0,politics
ভাই ডিজিটাল মন্ত্রী আর গোপন অায় হিসাব নিবে কে নিলে বল্লে অাপনি হবেন জংগি বা জামাত শিবির,0,politics
নাটক কাকে বলেরে ভাই,0,politics
হাজার হাজার সাধারণ ছাত্র ছাত্রি লাঠি চোটা শুধু ফুসফাস করলে আমলিগের সন্ত্রাসিরা ভয়ে দৌরাতে থাকবে কিন্তূ কেন পারেনা সাধারণ ছাত্ররা শুধু মাইর খাই সন্ত্রাসীদের হাতে,0,politics
এটা জামায়াত ও বিএনপির চকড়ান্ত।,0,politics
শেখ হাসিনাকে ভারতের দালাল সভাপতি পদ থেকে বহিস্কার করা হোক,0,politics
আর কত ঘেন্না আর অভিশাপ নিবে ছাত্রলীগ?? ছাত্রলীগ ধবংস হলে তো আমাদেরই খারাপ লাগবে।,0,politics
এত সাধারণ রাস্তাঘট ঠিক করে,0,politics
ভাই তোমাদের জন্য অনেক দোয়া রইল।তোমাদের উদ্দেশ্য জেনো শফল হয়।,0,politics
আপনার মতো লোক যদি হাজার টাকার ঘড়ি পরতে পারে তা হলে বাংলা এখন হ্মমতা ধর লোক সেই হিসাবে কোটি দামের ঘড়ি পরলে আপনি টোল করতে পারেনা টোল করবে যারা টাকার ঘড়ি পরে নিজের চরকাই তেল দেন 😋😋😋,0,politics
নিজের উন্নয়নের জন্য শপথ নিছে,0,politics
পয়েতৃশ লাখ টাকা আয় লাখ টাকার ঘড়ি হা হা হা ।,0,politics
তার লেখা বই একসময় বই মেলার সর্বোচ্চ বিক্রিত বই।,0,politics
অরজিনিয়াল ভাবে ওবায়দুল কাউয়া,0,politics
হারাম টাকা,0,politics
হাইরে লিক,0,politics
আপনি একজন সত্তকারের বিরপুরুষ,0,politics
সালা গাজা খোর কি কয় ঠিক নাই,0,politics
ওবায়দুল কাদেরের সনাম একটা ভোট চুরি করে ক্ষমতায় গেছে শেখ হাসিনার মত একটা খারাপ লোকের সাথে গেছে ওদের কে জুতাপেটা করা দরকার,0,politics
বেগম খালেদা তিন বার না সোয়া দুই বারের প্রধানমন্ত্রী।,0,politics
কিসের বই লিখে ফাটাকেষ্ঠ,0,politics
আপনার বলার ভংগি এবং বিষয়বস্তু খুব ভাল লাগে । এসব ভাবতেও খারাপ লাগে !!!!!,0,politics
জয় জয় বিএনপি,0,politics
নুরুল ভাইয়ের কিছু হলে দেখ যাবে রসাতল জাগো বাঙালি জাগো,0,politics
আমার ঘড়ির দাম টাকা আমি তাতেই গর্বিত,0,politics
কাক যখন ময়ূর হতে চায়।,0,politics
আরেক নাটক শুরু ভারতীয় দালালদের,0,politics
বেগম জিয়া তো বড় কাদের কি,0,politics
বিনা ভোটে নির্বাচিত হওয়া সরকার এর মন্ত্রী স্যার আপনার মতো স্পষ্ট ভাষী মানুষ এর খুব অভাব এখন এই দেশে,0,politics
কিচ্ছু করার নাই আমরা শুধু চেয়ে চেয়ে দেখব,0,politics
শাহেদ ভাই আপনার কথার সুত্র ধরে বলি বর্তমান রাজনীতি বিদ সাধারণ মানুষের কি ভাগ্য বদলাবে নিজেরটা নিয়ে বাঁচে না,0,politics
ইনু মিয়া তুমি তুমার বউয়ের ভোটো পাবেনা,0,politics
কার সাথে কার তুলোনা করে কোথায় কাউয়া কাদিরয়া আর কোথায় বেগম খালেদা জিয়া,0,politics
কাউয়্যা এখন সিংঘাম হইসে! গায়ে কোট চোখে কালো চশমা! একদম অজয় দেবঘনের সুইপারের মত লাগছে ফাটাবাঁশটাকে!,0,politics
টাকার ঘড়ি উপহার দিয়ে কোন টেন্ডার পাওয়া যাবে??,0,politics
এগুলো দূনীর্তি দমন কমিশন কি চোখে দেখে না?,0,politics
দেখা যাবে কিছুদিন পরে আপনিও নাই। হয়তো ঘুম করে দিবে নয়তো ব্ল্যাকমেইল করে চুপ করে দিবে।,0,politics
চোর খুনি বীরাঙ্গনা এর সাথে জনপ্রিয় নেতা ওবায়দুল কাদের সাহেবের তুলনা হয় না। আরে চাপা বাজ তোর মা খালেদা এত জনপ্রিয় তয় দেশের কোটি কোটি মানুষ জেলের তালা ভেঙে ফুলের মালা গলায় দিয়ে বাহির কেন করে না ? ওই চোর মহিলার ছেলে তারেক জন্মদাতা মা খালেদা জিয়াকে দেখতে আসেনা তার জন্য আবার গলাবাজি। ওই রুমিন ফারহানা তুই কি দেখেছ একজন চিত্র নায়ক সালমানের জন্য এ দেশের মানুষ জীবন দিলো এরপর সনে শেখ হাসিনাকে বাঁচানোর জন্য মানব ঢাল তৈরী করেছে তোদের গ্রেনেড হামলার সময়। তোরা শুধু পারো টিভির সামনে গলাবাজি করতে। আমিও লন্ডনে থাকি জানি তোদের তারেক এখানে মহা আনন্দে জীবন যাপন করিতেছে তার মেয়ে বয়ফ্রেন্ড নিয়ে রাস্তা আর ক্লাবে ঘোরে অথচ বৃদ্ধা দাদিকে দেখার জন্য দেশে যায়না। ওই তারেক সালা আর এক চোর নিজের মা এমনকি একমাত্র ভাইয়ের লাশটাও দেখতে গেলোনা। তোরা নির্লজ্জ যে চুরির দায়ে হাজতে তার জন্য বড় বড় কথা বলো ছিঃ ছিঃ।,0,politics
অধ্যাপকরাও দালালী করে।,0,politics
বতর্মান সময়ে খালেদা জিয়ার সঙ্গে কোন রাজনৈতিক নেতা নেএীর কোন তুলনা হয় না। কাউয়ার কথা তো আসতেই পারেনা।,0,politics
আমি তো নিজেই জানি না লাইসেন্স আসল কি নকল ।,0,politics
আরে ভাই ইনি কি বাল বলবে কিছু বলরে ওনার উপার কালকে হামলা করবে,0,politics
হে আল্লাহ তুমি রহম করো সব বন্ধুদের কাছে অনুরোধ জানাচ্ছি সবাইকে সবাই তাদের হাত থেকে মুক্তি করার চেষ্টা করো কারণ সে হলো আমাদের বাংলাদেশের প্রকৃত সম্পদ তাকে নিয়ে আমরা গর্ব করতে চাই,0,politics
ভালো তো ভালো না,0,politics
আমাদের বাংলাদেশের প্রত্যেক মহলের লোকেরা কোনো এক ভালো রাষ্ট্রের অনুসরণ করলে অথবা ভালো একটি ধর্মের অনুসরণ করলে সান্ত হয়ে যাবে। কোনো আন্দুলন লাগবেনা। আর আল্লাহ্ মনোনীত ভালো ধর্ম হলো একমাত্র ইসলাম দর্ম। আসুন সবাই একবার হলেও ব্যবহার করে দেকি। এর জন্য দরকার কৌমিমাদ্রাসা শিক্ষকত উস্তাদ ওছাত্রের। ধন্যবাদ,0,politics
ওবায়দুল কাদের সাহেব সাধারণ সড়ক মন্ত্রী। সাধারণ শব্দটা এতো জোর দিয়ে বলার কি হলো?? আপনি নিজে কার ছিড়েছেন?? শুধু টকশোতে এসে টেবিল গরম করতে পারেন।,0,politics
অপু উকিল গাঁজা একটু বেশী খেয়ে পেলেছে।আপনারা মাইন্ড করিয়েন না।,0,politics
ওবায়দুল কাদেরকে দেখতে মনে হচ্ছে চুর,0,politics
রাইট আপু,0,politics
এই খমতাটা যদি ইসলামের কাজে লাগানো হতো,0,politics
নুরুর উপর হামলা কারির কি বিচার হবে সৌরচার সরকারের,0,politics
চোরের আর এক নাম তারেক খালেদা।,0,politics
কি শিক্ষা দেয়া হচ্ছে? ভবিষ্যৎ কি?,0,politics
হাই রে ভালো কাজ করে এই রকম অবস্থায়,0,politics
সৎ ও যোগ্য নেতৃত্ব দরকার দরকার বাংলাদেশ এর স্বার্থে কাজ করা। এখন জনগন মনে করে ওবায়দুল কাদের সাহেব দিল্লির দিয়ে তাকিয়ে থাকে!,0,politics
অ সাধারণত,0,politics
আমি সবগুলা কমেন্ট পড়লাম সবার মতামত দেখলাম অনেকে ছাড়ে গালাগালি করতে দেখলাম কমেন্টের ভিতর কিন্তু ছাত্রলীগের স্যারকে জিম্মা করে রেখেছে কারণ ওরা তো ছাত্র হতে পারেনা ওরা হলো সন্ত্রাসবাদি আমরা বাংলাদেশে সন্ত্রাসবাদি দেখতে চায় না এইগুলা বন্ধ করেন,0,politics
আজকে মিডিয়া বাহিনী কুওার মত দৌরায় আর সারা বাংলাদেশে এত বড় একটা আন্দলন হইল। কোন মিডিয়ার কুওাদের দেখা জায়নাই।কাদের সাহেব আগেই মিডিয়া খবরদিয়া অবিজান পরিচালনা করতেছেন আর কত হাস্যকর নাটক বানবেন বন্দ করেন এগুল আর দেখতে চায়না জনগন।,0,politics
আললা তোদের বিচার করবে মিথ্যা বাদি,0,politics
অপু মদ খাইছে,0,politics
আপনাকে হাজার সালাম,0,politics
অপু উকিল ম্যাডাম তারেক জিয়া চুরি করেছিল বলে কি আপনারা ডাকাতি করবেন?,0,politics
সব ধরনের পাঠকের কথা মাথায় রেখে ভিডিও বানাতে হবে ভাই। যারা শুধু রংঢং পছন্দ করে তাদের জন্য বানালে হবেনা। আর এতদিন ভিডিও বানাচ্ছেন অথচ সাউন্ড কোয়ালিটির প্রতি উদাসিতা বেশ হতাশাজনক। ধন্যবাদ।,0,politics
অসাধারণ ‌!!!!!,0,politics
ভাই এই সম্পর্কে সাহেদ ভাই তার এ আলোচনা করেছেন।,0,politics
অপু উকিল তোমরা কোন ধরনের নির্বাচনে হয়েছো?????? মিড়িয়ার সামনে এসে মিথ্যাচার করতে লজ্জা লাগে না ????অপু তোমার কথা শুনে কাউয়াও লজ্জা পাবে,0,politics
দেশমাতার মক্তি চাই,0,politics
যার লাইসেন্স নেই সে কাদেরের হাতে টাকা দরাইয়া দেন ছাইরা দিব,0,politics
ইনু সায়েব কে কেউ পারলে এক বোতল বিশ দেউ,0,politics
আফগানিস্তান সরকারের উচিৎ বাংলাদেশ হতে কিছু ইনু জাতীয় নেতাদের নিয়ে দেশ পরিচালনা করা তাহলে তাদের দেশে কোন জঙ্গি থাকবে না,0,politics
মেয়ে গুলার মা বাপ নাই।,0,politics
যাদের পেট ভরে গেছে তারা অনায়াসে যাতে দেশ ত্যাগ করতে পারে তারই ধারাবাহিকতার প্রথম ভাগ এটি আস্তে আস্তে সবাই চলে যাবে পরি শেষে দেশ শূন্য করে অনুপ্রবেশ কাড়িদের হাতে তুলে দিয়ে সবাই পাড়ি জমাবে বিদেশে এভাবেই চলবে বাংলাদেশ ।,0,politics
ভাই আমি ঘড়ি পড়িনা,0,politics
অপু তোরে উকিল কে বানাইছে তুই তো ভাসাই জানচ না,0,politics
ব্যারিস্টার রুমিন ফারহানা কথা গুলি রাইট। অপু উকিল এর কথা ও রাইট তারেক মিয়া চুরি করছে ইন্ডাস্ট্রি করছে এই দেশের লক্ষ বেকার কর্ম সংস্থান পেয়েছেন কিন্তু বর্তমানে ব্যাংক গুলি লুট হল শেয়ার বাজার লুট হল টাকা গুলি কই গেল ইয়াতিমের কুটি টাকা খালেদ যিয়া খাইল কিন্তু সেটা এখনো এই দেশে ব্যাংকে আছে বছর আগেও গরুর গোস্ত টাকা ছিল আয টাকা সব কিছু ই গরিব দের নাগালে র বাহিরে আমার লেখা য় অনেকে ভাবতে পারে আমি বি এন পি করি না আমি হাত পাখায় ভোট দিতে গেছিলাম আওয়ামী লিগের মানুষ দিতে দেয় নি,0,politics
ফেরাউন বছর ক্ষমতায় ছিল তার পর কিভাবে ধংশ হয়েছে সবাই জানে যে এভাবে জুলুম করবে তার এই অবস্তা হবে,0,politics
টকশো না গজগ কি বললেন,0,politics
সত্য কথা বলতে সময় লাগেনা।সালা কুত্তালিগ কবে শেষ হবে?,0,politics
ছ্যাড় বড় অসহায় ছাত্রলীগের কাছে!!,0,politics
কাদেরের কিছুই নাই। তিনি যখন অসুস্থ হয়ে সিংগাপুর গিয়েছিলেন চিকিৎসা শেষে কাদের কাকু সিংগাপুরে নিজের বাড়িতেই ছিলেন। এইতো বেশি দিন হয়নি।,0,politics
আমার ঘড়ির দাম টাকা😥😥😥,0,politics
হালার পুতের কারনে দেশের সব জায়গায় তৃণমূল নেতারা নির্জাতিত।আর আমাদের ফেনীর রাজনীতিতো পুরাই ধংশ করেছে কাউয়া কাদিরা।হেতের কারনে ফেনীতে হাইব্রিট নেতারা রাজত্ব করছে অথচ দলের দূর্সময়ে তৃনমূল নেতারাই হাল ধরে ছিলো।আজকে যে সমস্ত হাইব্রিট নেতারা রাজত্ব করছে দলের জন্য তাদের কি অবদান আছে দেখান?,0,politics
ভাই একটু সাবধানে থাইকেন। সত্য কথার ভাত নেই ভাই,0,politics
ভাই মিজানুর রহমান আল আজহারী কে নিয়ে একটা পোস্ট করবেন প্লিজ,0,politics
যে ফেরেস্তা সেটা না তাঁরাও দূর্নিতীবাজ ছিলো গুন গুম ধর্ষণের সাথে জড়িত ছিলো। বর্তমানেও আছে কিন্তুু আওয়ামেলীগ সালে ক্ষমতায় এসেছিলো তো এসব দুর্নীতি দূর্ভোগ কমাতে কিন্তুু তাঁরা অতিতের তুলনায় অনেক বেশি দূর্নিতী করছে। যতই দুর্নিতী করুক তাঁর পরেও সব কিছুর দাম কম ছিলো। এখন টাকার চাল টাকা টাকার বিদ্যুৎ টাকা। রর্তমানে মানুষের বেতন বেড়েছে ডবল। কিন্তুু জিনিসের দাম বেড়েছে গুন। দুর্নিতী তাহলে কে করেছে??,0,politics
আর একটু আপেকা কর তোরে চাএলিগ খাইব,0,politics
একেকটা কুলাংগার।।।,0,politics
শেখ হাচিনা যদি কোন শত মা বাবার সন্তান হয়ে থাকেন তাহলে ইনু মিনুর বিচার করবেন কারন তারাই শেখ মজিব হত্যা প্রধান নায়ক,0,politics
ওর বক্তব্যের পরিপ্রেক্ষিতে মানুষ বিচার করবে,0,politics
এখন কাদের সাহেব বলবেন এইগুলো আসল না পাটুয়াটুলির কপি মাল,0,politics
ভাই সম্পদ মাএ গুন বেরেছে ! না না ¿?এটাও বিরুদ্বি দলের ষড়যন্ত্র কথা ক্লিয়ার না কোন ভেজাল আছে ধন্যবাদ 💚❤,0,politics
পাগলা নুরু আবারও পাগল হয়ে গেল নাকি কিযে হবে ঢাকা বিশ্ববিদ্যালয়ের। এখানে কি পড়াশোনা হয় নাকি শুধু পাগলামি ও মারামারি করা হয়।,0,politics
একটু কম চাটাচাটি কর বেশী চাটলে তীতা হইয়া যাইবো। বত্ মান বাংলাদেশে সবচেয়ে বড় জঙ্গী লীগ ও প্রচালীত আইনশৃখলা বাহীনি,0,politics
আমাদের টাকা ভাই সব আমাদের টাকা হায়রে হায় । দেশের হোগা মারা এইটা একবারে 💯😭😭😭😭😭,0,politics
স্যার না বলে সালারে প্যান্ট খুলে ফেল,0,politics
ঢাকা বিশ্ববিদ্যালয় হাঁটবে কবে ?,0,politics
তুইজানুচ কি আচে,0,politics
টিক আপু বেগম জিয়ার। জয় হবে আপু বেগম জিয়ার। আমাদের মা।।।,0,politics
আমি কিছু বুঝি নাহ যে পুরা ভার্সিটির শির্ক্ষাথীদের চাইতে কি ছাত্রলীগের পোলাপান বেশি হাতে গোনা কয় একটা ছাত্রলীগের কুলাংগারদেরকে কী ভার্সিটির সব শির্ক্ষাথীরা মিলে কি পিটাতে পারে নাহ হাতে গুনা কয় একটা ছাত্রলীগের দেখে ভয় পাওয়ার কি আছে 🤔🤔🤔,0,politics
বেগম জিয়া,0,politics
কোথায় কি বলেতে হবে আওয়ামীলীগ সে জ্ঞান রাখেনা। প্রধান মন্ত্রীর সাথে কাদেরের তুলনা হাস্যকর।,0,politics
আল্লাহ নুরু ভাইকে সকল বিপদ আপদ থেকে রক্ষা কর আমিন।,0,politics
আওয়ামী লীগ দলের একজন সাধারণ সম্পাদক ওবায়দুল কাদের সাহেব যখন তিনি অসুস্থ ছিলেন তার সুচিকিৎসার জন্য লক্ষ লক্ষ টাকা খরচ করে তাকে সিঙ্গাপুরে নিয়ে যাওয়া হয়েছিলো আর সেখানে বেগম খালেদা জিয়া কেনো সুচিকিৎসা পাবেনা কেনো তাঁকে সুচিকিৎসার জন্য বিদেশে নিয়ে যাওয়া হলোনা আমি কিন্তু কোনো রাজনৈতিক দল করি না কথাটা বলার প্রয়োজন মনে করেছি তাই বলেছি,0,politics
বরত মান সময়ের ব্যাংক হিসাব বলেন নি কিন্তু,0,politics
কার সাথে কার তুলনা হাইরে মানুষের গ্যান,0,politics
হাইরে রাজনীতি ফকিন্নির পোলা আওয়ামী লীগে যোগ দিলেই কোটি টাকার মালিক। খুন করলেও খুনী হয় না। ধর্ষন করলেও ধর্ষক হয় না।,0,politics
আল্লাহ তুমি যদি লক্ষ টাকা আমাকে দেও তাহলে একটা ফ্লাট কিনবো😔😔😔😔😔😔😔😔😔,0,politics
ডীম লিগ এইটা হাসো কর,0,politics
দুর্নীতির টাকায় করলে কত কিছুই করা যায়?,0,politics
ওবায়দুল কাদেরে অনেক গাড়ি আছে নোয়াখালী টু ঢাকা,0,politics
ভাই কোন কিছু করার নেই এদেরকে তো হাসিনা কমতাই থাকার জন্য লালন করতেছেন তাই এবার আর বিচার নয় প্রতিবাদের জন্য তৈরি হোন আমাদের দোয়া রইল তোমাদের জন্য,0,politics
অপু উকিল সব সময় একটা কথা নিয়ে আসে ছেড়া সুটকেস আর কিছু বলতে পারেনা?,0,politics
আপনারা অতিরক্ত কথা বলেন জন্য আপনাদের একটা কথা গ্রহণযোগ্যতা পায় না। ব্যক্তিত্ব নিয়ে একজন ভিক্ষুক ও খালেদা জিয়া কে ছাড়িয়ে যেতে পারে পক্ষান্তরে যুক্তরাষ্ট্রের প্রেসিডেন্টের সম্ভব নয় কথা বলার সময় একটু চিন্তা ভাবনা করে বলবেন,0,politics
জয় মামা কত টাকার মালিক একটু জানাবেন সেয়ার বাজার পদ্ম সেতু ব্যাংক হলমার্ক হাজার হাজার কোটি টাকা পাচার একটু শিকার করেন অপুআফা,0,politics
স্যার এর সংগে ছাত্ররা একমত না হলে না হতে পারে কিন্তু স্যার এর মুখের উপর আংগুল তুলে কথা যারা বলে তারা নিঃসন্দেহে বিয়াদোপ।,0,politics
থাক সাহেদ ভাই বাদ দেন!! বেডার একটা পোলাপান ও নাই এত্ত অবৈদ সম্পদ খাইবো কেডায় 😆।,0,politics
এত খারাপ হতে পারে মানুষ যা ভাবলে অবাক লাগে।এই বাংলাদেশে ভালো মানুষেরা বেচে থাকতে পারবে না,0,politics
অবৈধ বিনাভোটের গভীর রাতে দলবাজ পুলিশদিয়ে ভোটচুরি কারি নিলজ্জ হাচিনার পাচাটা কুকুর কাউয়া কাদিরাকে গনদৌলাই দিন ঔরা বাংলাদেশকে জিম্মিকরে লুটেপুটে খাচ্ছে।।,0,politics
ধন্যবাদ ভাই সত্য বলার জন্য উনি হচ্ছেন বাংলাদেশের এক নম্বর দুর্নীতিবাজ,0,politics
কত শত কোটি টাকার মালিক সে তা সেই ভাল জানে।,0,politics
আর আমাদের গ্রাম গরুর মাংস কিনতেও কষ্ট হয়ে যায়।,0,politics
কাওয়া কা জনগনে টাকা খাও,0,politics
ওহুরে খাদের ভাই কি মজা কালী মেশিন আর মেশিন রে ভাই,0,politics
হাঁটে হাঁড়ি ভেঙেছেন!,0,politics
অপু উকিল কে বলতে দিন না হয় বয়স না হলেও বারিয়ে রাজাকার বানিয়ে দিতে পারে,0,politics
আওয়ামীলীগ দের কে বলছি মদ খা মানুষ হ কই বেগম খালেদা জিয়া আর কই কাউয়া কাদের হাস্যকর হা হা হা হা,0,politics
শেখ হাসিনা বছর ক্ষমতায় থাকক তবে জনগনের আশা পূরন করে এভাবে নই। যেমন এরদোগান পুতিন।,0,politics
কাউয়া কাউয়া ভাইরে ভাই কাউয়া,0,politics
আপনি কি জানেন বাংলাদেশের মানুষ তিন বেলা খেতে পারে না??? আপনি তো আমাদের দেশ কে ছোট করেছেন,0,politics
আমি কোথাও শুনেছিলাম এ্যানা বাস কম্পানির বেশ কিছু শেয়ার আছে কাদের সাহেবের।,0,politics
মাননীয় প্রধানমন্ত্রী শেখ হাসিনাকে অসংখ্য ধন্যবাদ এই ইনু মিনুকে মহামান্য মন্ত্রী সভায় নারেখে মন্ত্রী পরিষদ গঠন করেছেন।,0,politics
বড় ভাই আপনার ভিডিওর অপেক্ষায় সব সময় থাকি কারন আপনার কথার যুক্তিগুলো খুব ভালো লাগে,0,politics
অপু মিথ্যা বলতে হলেও পারদর্শী হতে হয়। তুমি তো মিথ্যা বলতে ও শিখনি,0,politics
ছাএলীগ কে বাংলা দেশের মাটি ও জনগণ ঘৃনা করে,0,politics
সাহেদ আলম ভাই আপনি ইসলাম সম্পর্কে যা বলেছেন তা ঠিক না। ইসলাম ধর্ম ভাল ভাবে পড়ুন এবং জানুন।,0,politics
ছিঃ লীগ এত্ত নোংরা হয়ে গেছে।,0,politics
শেখ হাসিনা কেন বাদ যাবে না????,0,politics
লুটে পুটে খাচ্ছে এই সরকার এটা কনো সন্দেহ নাই,0,politics
জিয়ার বৌ তাই প্রধান মন্তুী হইছে তা ছারা কোনো যোগ্যতা নাই ৷,0,politics
বিশ্ববিদ্যালয়ের শিক্ষক সবার সামনে মিথ্যা কথা বলে তার কাছ থেকে ছাত্রছাত্রীরা কি শিখবে?? হায়রে বাংলাদেশ,0,politics
খালেদা বাংলাদেশের মৃ্র্খ প্রধানমন্ত্রী ছিল। দেশটাকে রাজাকর বানাইতে চেয়ে ছিল। সে জন্য এখন জেল খেটে মরে যাচ্ছে।,0,politics
জাতির লজ্জা।,0,politics
আওয়ামিলীগ বি এন পি দুই দলেই নতুন সভাপতি দরকার,0,politics
জুতা মারি তোর ভোট চোর হাছিনার কপালে,0,politics
সহমত নুরুর সাথে,0,politics
চল এ পূর্নিমা রাতে পালিয়ে যাই !,0,politics
সবার এরক কাজ করা উচিন কিন্ত এক দিন না,0,politics
জনার জন্য বোজার জন্য এরকম অনুস্ঠান ভাল লাগল।,0,politics
ইস্কন ভাগা তাইলেই হবে।,0,politics
ইনু কই?,0,politics
যত্তসব আজাইরগা বিষয় আপনার কাছে আরো ভালো কিছু আশা করি,0,politics
ওবায়দুল কাদের খয়রাতের মন্তি,0,politics
এখন চামচামির তেল বের করবেন মনে করে দেখ ইমরান সরকার কি করেছিল আর এখন হাসিনা তাকে কি করেছে,0,politics
এই সমস্ত অপুরা ভোট ডাকাত সরকারের তৈল মর্দন ছাড়া আর কিছুই করতে পারেনা!! এদেশে অপুদের বিন্দু পরিমাণ যোগ্যতা নেই নির্বাচিত হওয়ার! কেবল হাসিনার চুলে ধরে ঝুলে আছে নিজের অস্তিত্ব নিয়ে। অপু কাদের কুকুরের চেয়েও নিকৃষ্ট।।,0,politics
কি হচ্ছে ঢাকা বিশ্ববিদ্যালয়????,0,politics
অনেক খারাপ লাখছে😭😭😭,0,politics
ঢাকা বিশ্ববিদ্যালয়ের অন্যায়ের বিরুদ্ধে প্রতিবাদের ঐতিহ্যকেে ধ্বংস করে দেয়া হচ্ছে। এভাবে সমস্ত সেক্টর নীতিগতভাবে পঙ্গু করে দেয়ার ভারতীয় ষড়যন্ত্র সফলকাম হতে চলেছে। দাসত্ব অনিবার্য।,0,politics
এরা আওয়ামী ভাইরাস,0,politics
সাহসী সংবাদিকা সাবধানে থাকবেন।,0,politics
নুর কে ছাত্র সমাজের প্রধান ভিপি বানানোই হয়েছে সকাল-বিকাল পিঠানোর জন্য তা দেখে যেন দেশের যুব সমাজ ভীত হয়ে পথ চলে আর আগুন তো কোনো ভবনে ধরাচ্ছে না আতঙ্ক ছড়াচ্ছে জনগনের মনে ও মাথায়,0,politics
স্যার হালাদের পিডানো দরকার হালায় কয় ভুল বুঝাবুঝি ওর পুটকি দিয়ে ডিম ভরা দরকার,0,politics
নুরুর মা হাসিনাকে এইসন বলতে বলো,0,politics
অপু উকিল নিজেই একটা চরিত্রহীন মহিলা ! এই পতিতার নাপাক মুখে খালেদা জিয়ার নাম মানায় না! সে কিছু দিন আগে আমরা দেখেছি সুপ্রিম কোর্টের সামনে কিভাবে আইনজীবীদের উপর ইট পাটকেল নিক্ষেপ করেছে!,0,politics
দালালির ভাত নেই।,0,politics
ছাতরোলিগ ছারা অন্য ছাতরো ছাতরিদের গুনডালিকরা মেরেফেলবে দেশের মানুস জাগ,0,politics
এই ঘড়ি গুলো নকল! সাহেদ ভাই। আপনি ভাল ভাবে খুঁজে দেখেন। আর থলের কথা বলছেন সেঠা তো বিড়াল কালো । ভাই আমাদের মত গরীব দেশে মন্ত্রীরা খুব একটা দুর্নীতি করেনা! আপনি কি বলেন?,0,politics
ইউটিউবে লাভ রিয়েক্ট নেই কেন ❤❤❤❤❤❤,0,politics
ভিপি নূরকে আপনারা একেবারে মেরে ফেলো কেন এরকম কষ্ট দিচ্ছেন তিলেতিলে মারছে একবারে মেরে ফেলে সবচেয়ে ভালো হয় আপনাদের ক্ষমতা কিছুই হবেনা মেরে ফেললে,0,politics
এই হচ্ছে দুর্নীতিবাজ ফাটাকেষ্টর অবস্থা!,0,politics
হাসিনা সরকার কি ইনুছারা কি অচল,0,politics
টাকা দিয়ে কিনতে পারে না বাল এর মন্ত্রি।,0,politics
আসোলেই কাদেরের তুলনা হয়না কারন কাদের তো মুক্তিযোদ্ধা।একজন মুক্তিযোদ্ধার সাথে একজন নেত্রীর কোন তুলনা হতে পারেনা।,0,politics
এত টাকা দামের করি আছে ভাই আমার বিশ্বাস হয়না,0,politics
শেখ হাসিনা সাথে বেগম জিয়ার তুলনা করা যায় না আর কোথাকার কাউয়া,0,politics
সডকের মধ্যে খানে গাডী না দাডিয়ে। রাসতার বাম পাশে গাডী থামিয়ে লাইসেন্স চেক করতে হয়। এ আইন কি বাংলাদেশে নাই !!,0,politics
নুর ভাই কে হেফজত কুরুর আল্লাহ,0,politics
আওয়ামী দালাল বাংলাদেশ চলচ্চিত্র,0,politics
পরুক না একটু শখ করেছে ।মারুক না একটু নুরুরে পাতানো নির্বাচন নাইলে একটু জয়ী হলোই তাতে কি? একটু একটুই আর কি ।।হায়রে ভীতু বাঙালি !,0,politics
মাননীয় প্রধানমন্ত্রী অনেক কথা বলে এটা দেখে না নাকি উনি করাচ্ছে তলে তলে আমরা সব বুঝি জয় হক নুরু,0,politics
কই আকাঁশের তারা। কই হুন্ডের হেরা। কই খালেদা জিয়া।কই কাদিরা,0,politics
তারেক রহ মাব চে,0,politics
ভাই সেই হইচে,0,politics
ছাত্রলীগ তারাই করে যাদের ঘরে ভাঁত খাওয়ার জন্য চাউল ছাত্রলীগের নাম দিয়ে খাবার জুগার করে কিছু নেতার পাওয়ার নিয়ে,0,politics
সোহেল তাজ কে সাংগঠনিক সম্পাদক করা হোক,0,politics
এই যাবৎ কালের সেরা সাহসী ইউটিউবার,0,politics
যারা তাকে সৎ বলে তারা জাস্ট পর্দায় দেখেই বলে। আমি তার বাস্তব ইতিহাস জানি অনেক। ওবায়দুল কাদের এবং তার ভাই মির্জা তাদের চাচাকে হত্যা করেছে। তাই তার বাবা তাকে ত্যাজ্য করেছে। আমার কথায় সন্দেহ হলে তার এলাকায় গিয়ে খোঁজ নিয়ে দেখুন। ওবাইদুল কাদেরের বোন রোকেয়ার ঘর দোচালা টিনের এখনো। অথচ শালা কোটি টাকার ঘড়ি পরে। আমি কোন এক সূত্রে তাদের বাড়ির কাছে অনেকবার গিয়েছি এবং সেখানকার লোকজনের কাছে শুনেছি এসব।রোকেয়ার ঘর নিজ চোখে দেখেছি।,0,politics
হাসিনার উপর আল্লাহ গজব দেও,0,politics
দিন দিন পরিবেশটা নষ্ট হচ্ছে ।,0,politics
সোহেল তাজ কে সাধারন সম্পাদক দিলে ভাল হবে? কারন ওনি দুরনিতিকে থেকে বিরত আছে,0,politics
আপনারা বলতে পারবেন এখানে কোন মহিলার জন্ম পতিতালয় ????,0,politics
গত নির্বাচনে আমরা নৌকায় ভোট দিয়েছি নেত্রীর নির্দেশ এবং জননেতা মাহবুবুল আলম হানিফের কথায়আমি চ্যালেঞ্জ দিয়ে বলতে পারি ভেড়ামারা মিরপুর টোয়েন্টি ফাইভ পার্সেন্ট সেন্টারেও এজেন্ট দেয়ার মত ক্ষমতা ইনু রাখে না সেই ইনু বড় বড় লেকচার দেয়,0,politics
কাওয়া কাওয়া !!!,0,politics
বিচি ছাড়া স্যার,0,politics
ওয়ার্ড ও ইউনিয়ন পর্যায় এই কার্যক্রম করা উচিত কেননা স্বার্থের লোভে বর্তমান প্রতিনিধি ইউনিয়ন ও ওয়ার্ড পর্যায়ে বিভিন্ন রকমের কাজ করছে,0,politics
কাদের ভাইকে আরেক টা বিয়ে করাতে হবে নাহলে পাগল হয়ে যাবে পদ হারিয়ে । 😃,0,politics
নূর তুমি আগামী বাংলাদেশ,0,politics
আল্লাহর গজব পরুক হে আল্লাহ আপনি ছাএলীগকে ধংস করুন ৷ আমিন,0,politics
যিনা কাকে বলে কোন কাজ গুলো যিনা??✔ লজ্জা না করে আমাদের সকলের জানা উচিৎ! হে মুসলিম ভাই ও বোনেরা! জাহান্নামের কঠিন আজাব থেকে বাঁচতে চাইলে এখনি নিজেকে শুধরাও! নিজের আবেগ আর মন গড়া যুক্তি দিয়ে জাহান্নামের আজাব থেকে বাঁচা যাবেনা! যিনা কী ? শুধুই অবৈধ ভাবে মেলামেশা করাকে বলা হয়? না! ✔যিনা বহু প্রকারে বিভক্ত。✔ । কোন বেগানা নারী অথবা পুরুষের প্রতি দৃষ্টি দেওয়া চোখের যিনা! । যৌনতা সম্পর্কিত অশ্লীল কথাবার্তা বলা জিহ্বার যিনা! । বিবাহ সম্পর্ক ছাড়া অবৈধ ভাবে কাউকে স্পর্শকরা হাতের যিনা! । ব্যাভি চারের উদ্দেশ্যে হেঁটে যাওয়া পায়ের যিনা! । সে সম্পর্কিত খারাপ কথা শোনা কানের যিনা। । যিনার কল্পনা করা ও আকাংখা করা মনের যিনা! । অতঃপর লজ্জাস্থান একে পূর্ণতা দেয় অথবা অসম্পূর্ণ রেখে দেয়! ✔ বুখারী মুসলিম সুনানে আবু দাউদ সুনানে আন নাসাঈ ✔ অথচ আমরা কেবল সর্বশেষ ধাপ টিকেই যিনা মনে করে থাকি!এবার ভেবে দেখুন আপনি এসব এর কোনো একটির সাথে জড়িত নয়তো? ✔যিনা হারামঃ✔ আল্লাহ তায়ালা যিনাকে হারাম ঘোষণা করে বলেনঃ তোমরা যিনার ধারের কাছেও যাবেনা।কেননা তা অত্যন্ত নির্লজ্জ এবং খারাপ কাজ।” সুরা বনী ইসরাঈল আয়াতঃ ✔যিনার শাস্তিঃ✔ রাসুলুল্লাহ সা বলেছেনঃ “আমি স্বপ্নে একটি চুলা দেখতে পেলাম যার উপরের অংশ ছিল চাপা আর নিচের অংশ ছিল প্রশস্ত আর সেখানে আগুন উত্তপ্ত হচ্ছিল ভিতরে নারী পুরুষরা চিল্লা চিল্লি করছিলো! আগুনের শিখা উপরে আসলে তারা উপরে উঠছে আবার আগুন স্তিমিত হলে তারা নিচে যাচ্ছিলো সর্বদা তাদের এঅবস্থা চলছিলো।আমি জিবরাঈল আঃ কে জিজ্ঞেস করলামঃ এরা কারা??? জিবরাঈল আঃ বললেনঃ তারা হলো অবৈধ যৌনচারকারী নারী ও পুরুষ। বুখারী যিনা কারীর লজ্জা স্থানের দূর্গন্ধে জাহান্নাম বাসী অস্থির হয়ে উঠবে। সেদিন যিনা কারীকে পিপাসা মেটানোর জন্য এই পঁচা পানি দেওয়া হবে। তাই সবারই উচিত প্রেমিক প্রেমিকা নামের এই শয়তানি সম্পর্ক বাদ দেওয়া! কারন হাশরের ময়দানে এই সব শয়তানী সম্পর্ক থাকবে না। থাকবে শুধুই আগুন! সেদিন কেউ কাউকে চিনবেও না আর বলবে হায় আফসোস! আমি যদি রাসুলের দেখানো পথে চলতাম সুরা ফুরকান আয়াত জালেম সেদিন আপন হস্তদ্বয় দংশন করতে করতে বলবে হায় আফসোস! আমি যদি রসূলের সাথে পথ অবলম্বন করতাম। অমুক বন্ধুর ডাকে সাড়া না দিতাম তাহলে আজ আমার এ দশা হতো না। “যদি কেও না জেনে এই অপরাধ করে থাকে!এবং খাস দিলে আল্লাহর কাছে তাওবা করে তবে আল্লাহ পাক তাকে ক্ষমা করে দিবেন! ইনশাআল্লাহ সুরা ফুরকান আয়াতঃ “হে আল্লাহ এমন গুনাহ্ থেকে আমাদের সকলকে হেফাজত করুন!【 আমিন 】 ? ব িদ্রঃ– ইসলামের সার্থে শেয়ার করে সকলকে জানার সুযোগ করে দিন।,0,politics
সালা যখন মরবে টাকা নিয়া কবরে যাবে এটা বেশিদিন দুরে নায়,0,politics
দেশের বাইরে থেকে একটা ইউটিউব চ্যানেল খুলে এভাবে মন্ত্রিদের নিয়ে কথা বলায় যায়। 😂😂,0,politics
কাওয়ার বাসায় কি না পাওয়া যায়! হতে পারে সেকেন্ড হ্যান্ড অন্যের ঘর থেকে চুরি করা ।,0,politics
এখানে শেখ হাসিনাকে দেখতে ফেরাউনের মমি চেহারা যেরকম সে রকম দেখাচ্ছে আস্তে আস্তে ফেরাউনের সুরত চলে আসতেছে জয় বাংলা,0,politics
হায়রে কপাল কোথায় বেগম জিয়া আর কোথায় কাওয়া কাদের।,0,politics
ঘড়ি পরেছে তো কি হয়েছে স্বর্ণের কোট তো আর পরেনি ওনার দারা স্বর্ণের কোট পড়ার মতো টাকাও আছে ।,0,politics
ওবাইদুল কাদের আমারও প্রিয় নেতা ছিলো। কিন্তু এখন আর সয্য হয় না,0,politics
গ্রাম্য ভাষায় একটি প্রবাদ বাক্য আছে কোথায় তাল গাছ আর কোথায় বাল গাছ ঠিক তেমনি ভাবে বেগম খালেদা জিয়া হচ্ছে তাল গাছের মতো বটবৃক্ষ যার ওপরে সীমাহীন ঝড় বৃষ্টি বয়ে গেল তাকে কোনমতে নোয়ানোর যায় না তাল গাছের সাথে কলাগাছ মান্দার গাছের তুলনা করে লাভ নেই বোকামি ছাড়া,0,politics
এগ কথা কে শুনে। মিথ্যা আর ধোঁকাবাজি সাথে যাদের সম্পর্ক।,0,politics
এইযে লোকটা সোগান দিলো জালোরে জালো জগলী সোলগান এটি,0,politics
এটা হাস্যকর আলাপ।,0,politics
উনি দেখতে এসেছেন উনার মত আর কার কার কাগজপত্র নাই,0,politics
হা হা হা কই আগার তলা আর কই উগারতলা,0,politics
আপনারা ভুলে গেছেন মনে হয় তারেক জিয়ার একটা শার্টের দাম লক্ষ টাকা,0,politics
বিরধিদলের ব্যবহার কে শৈল্পিকতার পর্যায়ে নিয়ে গেছে ✌✌✌,0,politics
এটা তুমি এতদিন বাদে পাইছো ভাইয়া,0,politics
ফোড়ায় কষ্ট😂😂,0,politics
কথার অগোছালো জড়তা প্রমান করে। তোর সময় খুব কাছে ডাস্টবিন হবে তোর বাসস্হান।,0,politics
বাটপার দূদক কোথায় এখন।ওরা এসব দেখেনা?,0,politics
বিশ্ববিদ্যালয় এর আন্দোলন এ যদি স্কুল কলেজ এর ছাত্র ছাত্রীদের এগিয়ে আসার সুযোগ দেওয়া হতো তাহলে দেখিয়ে দেয়া যেত ছাত্র শক্তি কাকে বলে,0,politics
এই আবালরে ভিপি বাইনাইয়া দেশের ভিতরে অজাথা একটা ঝামেলা করতেছে এখানে একজন যোগ্য লোকের প্রয়োজন ।,0,politics
খবর দেখার আগে কমেন্ট পড়েছেন কে কে??????,0,politics
চামচামি শেষ ডাসবিনে ফেলে দিবে সময়ের বেপার,0,politics
বাংলাদেশের দ্রুভ রাঠি,0,politics
? এ আপনি বলেছেন বাংলাদেশের প্রথম রাষ্ট্রপতি সৈয়দ নজরুল ইসলাম !!! ভেবে দেখেননি ভারপ্রাপ্ত বলা উচিত ছিল।,0,politics
আল্লাহ তায়ালা সবায়কে হেদায়েত দান করুক আমিন ❤💚❤,0,politics
ধন্যবাদ বস,0,politics
ডিম লীগের কামরা কামরির কারনে দেশটা আজ অধপতনের শীকার।। তাই এতো গজব হচ্ছে।।,0,politics
সাবাস বড় ভাই💛 ভালো লাগছে খুব।,0,politics
ভাই চালিয়ে যাও তোমার থেকে আমরাও কিছু জানবো এবং শিখবো।,0,politics
ওবাইদুল কাদের লাখ লাখ টাকার ঘড়ি পরবে তাতে আপনাদের সমস্যা কি?ওবাইদুল কাদের একজন বড় মাপের রাজনিতিবীদ মানে তিনি একজন লাইসেন্সধারি বড় চোর এবং ডাকাত তাই তার অনেক টাকা আছে তাই উনি লাখ লাখ টাকার ঘড়ি পরতেই পারেন আপনাদের লাখ লাখ টাকার ঘড়ি পরতে ইচ্ছা করলে আপনারাও বড় রাজনিতিবিদ হন এবং দেশ লুটপাট করেন এবং কোটি টাকা দিয়ে ঘড়ি কিনেন এবং যা ইচ্ছা তাই করেন সমস্যা নাই।,0,politics
হাহাহা ইনু,0,politics
ভাই এগিয়ে যান আমরা আছি আপনার পাশে।,0,politics
এই রকম ভিডিও বানিয়ে যান ভাই।,0,politics
সবসময় তোমাকে ভালোবাসি ভাই। সত্ত তুলে ধরো তাই।,0,politics
কাদের চুরি করতে করতে গলা সমান এসে গেছে তারপর ও চুরি করা ভূলতে পারে না।,0,politics
এই সব দামি ঘড়ি সুইজারল্যাণ্ডের বড় শহরের বিভিন্ন দোকানে দেখেছিলাম এই ঘড়ি কেনা আমার পক্ষে সম্ভব নয় একদিন দেখলাম একটা ঘড়ি স্ট্যান্ডের উপর রাখা আছে দাম লেখা ফ্রাঙ্ক খুশি হয়ে ভিতরে ঢুকে জিজ্ঞেস করলাম দোকানদার ভাই ঐ কম দামী ঘড়িটা আমাকে দিন তিনি উত্তরে বলেন ভাই ঐ টাতো ষ্টেন্ডের দাম রোলেক্সঘড়ির দাম ফ্রাঙ্ক উত্তরে কিছুই বলিনি হতাশ হয়ে বের হয়ে গেলাম কারণ আমার পক্ষে সম্ভব নয় এত দামী ঘড়ি ক্রয় করা সত্যঘটনা আমার জীবনে বের্ণ শহরের কৌতক নয় ! রাডো সেক্টর মোনদিয়া রোলেক্স ফ্যেরারী সবকয়টা দামী ঘড়ি !,0,politics
মজা পাইলাম রুমিন ফারহানার সাথে এই মহিলার যায় না,0,politics
উত্তরবঙ্গের রাস্তাঘাট খুবই করুণ সেই কবে থেকে।কেও নাই দেখার,0,politics
ওবায়দুল কাদের অনেক ভালো মানুষ তাই তোমাদের মতো মহিলাদের নিয়ে রাত্রি কাটায় সালি আওয়ামীলিগ দেশটাকে রসাতলে নিয়ে গেছে তারপরে ও বড় বড় কথা,0,politics
ভাই কিছু ভুলিনি! আর আমরা যদি ভুলেও যায় কেউ না কেউ সকল তথ্য সংগ্রহ করে রাখছে একদিন জাতির সামনে ঠিকই প্রকাশ করা হবে,0,politics
নুরতো হাসিনার ছেলে,0,politics
আপু উকিল রোজার বিতরে ইয়াবা খেয়ে আসছে,0,politics
সালা কাওয়া,0,politics
সাব্বাস! গরু মেরে জুতা দান প্রবাদটি মনে এ জন্যই তৈরী হয়েছিল।,0,politics
খালেদা জিয়াকে বাংলাদেশ লোক পছন্দ করে। আর আওয়ামিলীগ কে বাংলাদেশ লোক পছন্দ করে। কাদের কে ত জন্য লোক ও পছন্দ করেনা,0,politics
কাক ডাকা বন্ধ ।হবে,0,politics
আওয়ামী দালাল ।কাদের কি এমপি হওয়ার যোগ্য ।ক্ষমতার বলে মামলা নাই।তাদের কথা মতো বাংলাদেশের লক্ষ লক্ষ মানুষ হত্যা করা হয়েছে,0,politics
আই লাভ ইউ ।সবাই কে,0,politics
এই সরকারের আমলেই তোর ফাসী হবে এই বছরেই হবে,0,politics
ভাই আপনার ভিডিও র অপেক্ষায় ছিলাম।💘 হাফিজুর রহমান এবং আজহারী সাহেবের মাঝে চলমান দন্দ নিয়ে আপনার ভিডিও আশা করছি,0,politics
এগুলো আসলে সব পাটুয়াতলীর ঘড়ি! আর এসব এর মুল্য টাকায় নয়! নোয়াখালীর কারেন্সিতে হিসেব করতে হবে।,0,politics
কার সাথে কে আর পান্তাভাতে ঘে।,0,politics
সব শালারাই তো চোর কথায় আছে না মানুষ পাগল হলে বাধে রশি দিয়ে রশি পাগল হলে বাধবেন কি দিয়ে,0,politics
জেই দেশে আইন প্রয়ুগকারি তাকেনা সেইদেশে এইরকম খাওয়া কাদেরের নাটক দিয়েও কিচোহবেনা,0,politics
এখন ওদেরই সময়,0,politics
ভাই আপনি অনেক সাহস,0,politics
পাসের পুলিস টার দুধ কতো বরো বরো ওডা কি পুলিস,0,politics
কি বলে এরা? কাদের সে কে রে?তারে কে ছিনে রে?,0,politics
মে রা এস এম হলে কেন যায় তাদের কোন ছেলে নেতা নাই,0,politics
আওয়ামিলীগ এ চোরের অভাব নাই।হয়তো আরো নতুন প্রশিক্ষন প্রাপ্ত কোন বড় চোর কে সাধারণ সম্পাদক বানাবে।,0,politics
গিফ্ট কি এমনি এমনি দিয়েছে,0,politics
জাতীয় পায়খানার নাম বাংলাদেশ আওয়ামী লীগ!,0,politics
ওই মহিলা টা হয়তো আম লিগের সদস্য তাই সে বি এম পির নামে এই ধরনের কথা বাতো বলছে এইটা ঠিক নয়,0,politics
তাইতো বলি মাথা পিছু এত টাকা। কিন্তু আমার টাকা কই।।,0,politics
ভাই মনে হয় মুসলিম,0,politics
নুর ভাইয়ের জন্য দোয়া রইলো,0,politics
দিয়ে আদর্শবান নেতা চাই,0,politics
নিজেকে কি ওবায়দুল কাদের ভাবেন! আমি ওনাকে ভালোবেসে লক্ষ টাকার ঘড়ি দিলে আপনার কি সমস্যা আছে?,0,politics
আওয়ামী সরকার ভুয়া,0,politics
এদেরকে এনকাউন্টার দিয়ে ফেলে দেয়া হোক,0,politics
ব্যাপার না।।।।আমিই দিছি টা ঘড়ি তারে।সব করে।,0,politics
বেশ একটি মিল আছে ফাটাকেস্ট আর মালোয়শিয়ার সাবেক প্রধানমন্ত্রীর স্ত্রীর সাথে। ভদ্রমহিলা লুটের টাকায় পৃথিবীর সব বিখ্যাত ব্রান্ডের হ্যান্ডব্যাগ ও ঘড়ি কিনেছে যার একেকটি কোটি টাকার চেয়েও বেশী মূল্যের। ভেবেছিলো মানুষ বুঝতে পারবে না কিন্তু শেষ রক্ষা হয়নি।,0,politics
মৃষ্টি কথা বললেই ইনু তুই পার পাবি না,0,politics
আমার নাম রাহুল আরিয়ান আপন। আমি জর্জ ভাইয়ার এর একজন মডারেটর। আপনার চ্যানেলের প্রতিটি ভিডিও আমাদের খুব ভালো লাগে। সেইসাথে আপনাকেও আমরা খুব পছন্দ করি। আমাদের এই চ্যানেলে আমরা আপনার একটি নিতে চাই। যদি আপনার কোনও আপত্তি না থাকে। টি দেখানো হবে। মিনিটের এই এ আপনাকে শুধু প্রশ্ন করা হবে । এ আপনার আগমন কীভাবে ঘটলো? । আপনার এই চ্যানেল নিয়ে ভবিষ্যত পরিকল্পনা কি। । সেই সাথে জিজ্ঞাসা করা হতে পারে আপনার ভালো মন্দ বলা না বলা কিছু কথা। @,0,politics
বেগম জিয়া পারিবারিক কৌটায় প্রধানমন্ত্রী হয়েছেন! আর এবায়দুল কাদের এর বীর যোদ্ধা। ওবায়দুল কাদেরের বিরুদ্ধে কিংবা তার পরিবারের বিরুদ্ধ কেন দুর্নিতীর অভিযোগ নেই। আর খালেদা জিয়ার নিজে ও পরিবার এমনকি আত্ময়ীস্বজনে বিরুদ্ধেও দুর্নীতির পাহাড় সমান অভিযোগ। ওবায়দুল কাদের ঢাকা বিশ্ববিদ্যালয়ের শিক্ষকতাও করেছেন কিছুদিন আর খালেদা জিয়া ?,0,politics
হেতে ফাডাকেষ্ট।।।। 🤪🤪,0,politics
আল্লাহ নুরুল ভাইকে হেফাজত করুন,0,politics
ভোট চোর দের পরি বরতোন করলেই বা কি আর না করলেই কি,0,politics
আওয়ামী লীগ মানেই মিথ্যে কথা বলার একটা ফ্যাক্টরি,0,politics
ক্যাসিনো ব্যবসার ভাগ নিয়ে এসব দামি দামি ঘড়ি কিনেছেন ওবায়দুল কাদের সাহেব এটা সত্য,0,politics
এটা কোন ব্যাপার না জয় বাংলা 😂😂😂😂😂,0,politics
নৌকা ছাড়া ইউনিয়ন পরিষদের মেম্বারও হতে পারেনা সে আবার লাফা লাফি করে। নৌকায় অনেক কিছু নিয়েছেন পেয়েছেন শুকরিয়া আদায় করা উচিৎ।,0,politics
নতুন সাধারণ সম্পাদক কে হতে পারে??? সবার কী মনে হয়??????,0,politics
শেখ মুজিবুর রহমানের সাথে জিয়ার তুলনা কিবাবে হয় পাগলের দল,0,politics
ওবায়দুল কাদের নিজেও একজন দুর্নীতিবাজ বাংলাদশের বেশিরভাগ রাজনৈতিক নেতাই দুর্নীতিবাজ সঠিকভাবে অনুসন্ধান করলে বেশিরভাগ নেতাকেই জেলে যেতে হবে,0,politics
পাপ করলে সাজা হবেই,0,politics
খালেদা জিয়া বড়,0,politics
ভাই আপনি কাদেররে চিনেন! হালায় রাইতের বেলায় চাদর মুড়ি দিয়ে ফার্মগেটের তল থেইকা কিনছে। ওই হালার মতো ঘড়ি গুলাও নকল।,0,politics
ফালতু হেড লাইন দেয়।,0,politics
কুব সুন্দর এবং ভালো সিদ্দান্ত আদর্শ বান এবং নিতি আছে এমন নেতা সামনে আগামি দিনে দেখতে চাই । আদর্শ আছে এই রকম ব্যাক্তি কে পদে দেখতে চাই।।,0,politics
এগিয়ে যাও নুর ভাই আমরা আছি তোমার সাথে,0,politics
ছাত্রলীগ নামের সন্ত্রাসীদের বলছি এখনও সময় আছে তোমরা এইসব খুন খারাপি ছেড়ে ভালো হয়ে যাও কারণ মানুষের ক্ষমতা সারা জিবন থাকে না তাই মানুষের উপর জুলুম অত্যাচার বন্ধ করেন।,0,politics
বি এনপি ক্ষমতায় আসলে রাস্তা গাটে শহরে বমা আর বমা,0,politics
ছাত্রলীগ কি জানোয়ারকে হার মানানুর শপথ নিসে????,0,politics
যাহ বাল তোদের খাডেলা জিয়াও আমার বাল কাদের মুক্তিযুদ্ধের সময় জেলে থাকা অবস্থায় বাংলাদেশ ছাত্রলীগের সভাপতি ছিলো আর তোদের খাডেলা জিয়া পাকিস্তানি গো কাছে গিয়া কাম দিছে।মাগী রুমিন ফারহানা যে কার কার কাছে কাম দেয় সেইটা সবাই জানে,0,politics
ভাঙ্গা রেকর্ড আর কতো দিন বাজাবে,0,politics
ওর বাপ দাদার সম্পত্তি তাই পড়ে,0,politics
বাংলাদেশের জনগণের উপর আহ্বান করা হচ্ছে যে নুরুল ভাইয়ের ওপর যদি কোনো হামলা হয় আপনারা কেউ হাত হাত রেখে বসে থাকবেন না,0,politics
আমি ফার্মগেট থেকে ঘড়ি কিনেছি টাকা দিয়ে।,0,politics
দারুণ ! কে বলেছে বাংলাদেশ গরিব !!,0,politics
কে কে আল্লাহ পাক কে ভয় করেন??সাবস্ক্রাইব করে সাড়া দেন!! ?,0,politics
ভোটার বিহীন মুনতি তার নিজের লাইসেন্স নাই সে আবার অবৈধ লাইসেন্স ধরে,0,politics
মিথ্যে বলার একটা সীমা আছে।,0,politics
এদের অত্তাচার এ সাধারন মানুষ এর জীবন টা তেচপাতা হয়ে জাচ্ছে,0,politics
ভালো লাগলো একজন আর একজন কে গালি দেয়,0,politics
ওবায়দুল কাদেরের ভুলভাল বক্তব্য গুলো তুলে ধরার জন্য অনেক ধন্যবাদ এটা ক্লিয়ার করবেন ঘরি কি দেশের টাকা দিয়েছে না নিজের টাকা দিয়ে নিয়েছে,0,politics
নুর সালা এখনো আছে?,0,politics
এসব লোকের জন্য দলের ওসরকারের বদনাম হয়।,0,politics
এমাগিভুল,0,politics
আমি মনে করি এখানে এর মূল সিদ্ধান্ত নেওয়ার কারণ মুসলমানদেরকে সরিয়ে সরিয়ে নাস্তিকদেরকে দায়িত্ব দেওয়ার চিন্তাধারা করছে এই নাস্তিক সরকার আমার কাছে ঠিক এমনটাই মনে হচ্ছে যদিও সবাই আওয়ামী লীগ ভারতের দালাল,0,politics
প্রধানমনিত্র কোনো বিচার কি হবে?,0,politics
আওয়ামী লীগের সব নেতাই একই গোয়ালের গরু। কেউ একটু বেশি খায় কেউ একটু কম। এটাই,0,politics
কার লগে কি হালার বুঝলাম না,0,politics
ইয়েস আপু আপনাকে অনেক অনেক ধন্যবাদ জবাব দিতে বলে,0,politics
আওয়ামীলিগ জনগনকে ভোদাই মনে করেন!! আফসোস।,0,politics
স্যালুট ব্যারিস্টার রুমিন ফারহানা ❤,0,politics
শুধু কাউয়া কাদের ফাটা কেষ্ট কেন আওয়ামী সব মন্ত্রী মিনিস্টার আমলা নেতারা হাজার হাজার কোটি টাকার মালিক।শেখ হাসিনার পোলা আমেরিকায় টি বাড়ির মালিক প্রতিটি বাড়ির মুল্য থেকে কোটি টাকা। ব্যাংকে রয়েছে হাজার হাজার কোটি ডলার। শেখ হাসিনা দেশের মানুষের মুখে হাসি ফুটাবে। অথচ লুটপাট করে হাজার হাজার কোটি টাকা কামিয়ে তার দলের লোকেরাই হাসছে হা হা হু হু হি হি। শেখ হাসিনা ! বলতে পারবে একটা পরিবারের সুখের জন্য কতো কোটি টাকা চাই ?,0,politics
ভাই অসত্য মিথ্যা কথা বলা পাপ। ন্যয় এবং সত্যের পথে চলুন। কেন একজন সৎ মন্ত্রীর বিরুদ্ধে মিথ্যা কথা বলছেন। মুখ পবিত্র। কেন মিথ্যা বলে মুখকে অপবিএ করছেন।,0,politics
বাঘের সাথে ইঁদুরের তুলনায় করে,0,politics
সুপার রুমানা মেডম!!,0,politics
ডিম তারাপি দেওয়া হউক নুরুপাগলা কে আর ওর দুনু বউকে,0,politics
তুই দেশের জন্য কি করেছিস দশ হাজার টাকার গড়ি পরিস মানুষ তিন বেলা খেতে পারেনা,0,politics
রাজনীতিবিদরা বেশিরভাগ সময় এই জিনিসগুলো উপহার হিসেবে পেয়ে থাকেন।। এর চেয়ে অনেক দামি ঘড়ি পড়া অনেক পাতিনেতা আছে।।।,0,politics
কাদেরের সাথে পাগলের তুলনা করলে মানায়ত,0,politics
মুখেরের এমন না করে সোজা ভাবে কথা বলুন সামনে কি তেতুল আছে,0,politics
আমি আওয়ামিলিগ করি তার পরও বলছি ইনুকে আওয়ামিলিগ থেকে বাদ দেওয়াহুক,0,politics
সব সমান,0,politics
ডিম মার বেশি করে হাহাহা,0,politics
অসাধারণ,0,politics
কাকের তুলনা কাকের সাথেই করা উচিত,0,politics
আগে বড় বড় চুরি হতো । আর এখন হবে মহা চুরি।,0,politics
মন্ত্রিত্ব না পাইয়া পাগল হয়ে গেছে,0,politics
ওবায়দুল কাদের বাংলাদেশের তিন তিনবারের প্রধানমন্ত্রী বেগম খালেদা জিয়ার পায়ের জুতার সমান হওয়ার যোগ্যতা রাখে না এটা আমার সুস্পষ্ট বক্তব্য,0,politics
এরা নাকি দেশের সম্পদ। ওদের স্লোগান হচ্ছে আগুন জালো। এই শিক্ষাপ্রতিষ্ঠান এ আগুন জ্বাললে শিক্ষা নিবে কোথা থেকে।????,0,politics
আমি ছাত্রলীগের একজন সদস্য কিন্তু ইদানীং এর মাঝে ছাত্রলীগের কর্মকাণ্ড দেখে খুব খারাপ লাগতেছে,0,politics
ছোট মাছ ধরে লাভ কী? বোয়াল ধরেন দেশে অনেক বোয়াল আছে,0,politics
আওয়ামী লীগ একটি জিনিস বাবারে বাবা ইনু আর মিনু দিছে বাঁশ,0,politics
আমি এমেলে ফাটাকেস্টো আমি এমেলে ফাটাকেস্ট আজ এ মুভি টা দেখে আজ তিনি এ পরজায়ে,0,politics
ভিপি নূর বানিয়ে নিজেই এসব করছে সরকারী লোকদের বদলাম করার জন্য এবং সরকারের দেশে এবং বিদেশে বদলাম করার চেটা করছে,0,politics
সোহেল তাজ কে দেখতে চাই সাধারণ সম্পাদক হিসেবে,0,politics
বাংলাদেশর এক মাএ বাজে দল ছাএলীগ তারা নিজেকে কি মনে করে আপনি একবার ভাবেন তো যে দিন ক্ষমতা থাকবে না সেদিন কি হবে জানেন একবার ভাবেন ওকে,0,politics
ছাত্রলীগ বর্তমানে বাংলাদেশে একটি ভাইরাসে রূপান্তরিত হয়েছে মানুষের কোন আস্থা নেই বিশ্বাস নেই ভরসা নেই সুতরাং এগুলো সব কিছুই আপনারা গুজব মনে করেন কারণ এই সরকার ছাত্রলীগের উপর ভর করে আছে এবং পুলিশের উপর ভর করে আছে এবং গুজব শব্দের উপর ভর করে আছে।,0,politics
হাহা,0,politics
খমতার লোবে ওইক্ক করেছে বাবা খুনির সাথে,0,politics
ভাই কথার পিছনে মিউজিক টা না দিলে ভালো বুজা জাইতো। তবে অবিরাম ভালোবাসা রইলো,0,politics
ধন্যবাদ অনেক দিন পর একটা আলোচনা বিরক্ত ছাড়া শুনলাম,0,politics
তাইতো কই এতো মাং গেলো কই,0,politics
অসাধারণ একটি অনুসন্ধানী নিউজ। তাসনিম খলিলকে ধন্যবাদ।,0,politics
ভালো,0,politics
রুমিন ফারহানার সাথে এই মহিলার যায় না,0,politics
শেখ মুজিব কোন জমিদার ছিল,0,politics
আপনার কথার যুক্তি গুলো খুবই ভালো লাগে হিন্দু ব্রাহ্মণ এর মত ব্রাহ্মণ বলে কোটি দেবতা আছে যা বাস্তবে নাই আপনিও একটা নিউজ দেখেন নিজের থেকে মনগড়া কিছু সুন্দর করে উপস্থাপন করেন বাস্তবে জিজ্ঞেস করে উত্তর জেনে প্রচার করবেন বর্তমান সনাতন ধর্মের জামানা নাই,0,politics
শিক্ষা প্রতিষ্ঠান গুলা এখন নোংরা রাজনীতিতে ভরে গেছে।,0,politics
হে প্রশাসন তোমরাকি র্নিভোদ থাকবে কবে তোমরা বুজতে পারবে দেশে উন্নয়ন না শান্তির দড়কার।মানুষকে বোমা মেরে নয় ভালোবাসা দিয়ে বোজাতে হয়।তোমাদের বোমা বাজির উন্নয়ন এ দেশের মানুষ আজ অসান্তিতে।,0,politics
যে যেমন কথা বলনে তেমন।,0,politics
সময় গেলে সাধন হয় না দুইজন মারা জাওয়ার আগেই সচেতন হলে দু জিবন যেতো না,0,politics
আঈনির দিকে বিবেচনা করলে খালেদাকে যে হার সেবা দিচ্ছে সেদিক থেকে বলা যায় আঈন দূই রকম হচ্ছে সব কয়াতিকে সমান অধিকার দেওয়া উচিৎ না হলে প্রশ্ন আসবে বড় লোকের জন্য এক আঈন আর গরিবের জন্য আরেক আঈন এটা কি সংবিধানের অায়তায় আসে ?,0,politics
ঢাকা বিশ্ববিদ্যালয়ের শিক্ষক রাও দালালী শুরু করছে,0,politics
পৃথিবীতে কেঁউ সারাজীবন থাকেন না আর এভাবেই কোনো একদিন নাস্তিক এর বাচ্চারা বিদায় নিবে??,0,politics
বড় পরিবর্তন মানে নতুন নেতাদের পেটমোটা করা দেখো বাস্তু হয়ে না জাই,0,politics
প্রিয় শাহেদ ভাই আপনার কথা গুলি অতি মুল্যবান। তাই আপনাকে সেলুট জানাই প্রিয় ভাই ভালো থাকবেন আশা করি,0,politics
দুর্নীতি সন্ত্রাস চাঁদাবাজি চোরির আপর নাম জিয়া পরিবার,0,politics
হাসানুল হক ইনু কি পটকা বোম ফাটালেন না ছিটকা বোম ফাটালেন ?,0,politics
আমার ঘড়ির দাম মাত্র টাকা। কই টাইম তো ভুল দেখায় না সব ঠিকঠাক আছে,0,politics
কি ভাবে পারেন ভাই? অামি পুরাই শিহরীত,0,politics
কাউয়ার সাথে বেগম জিয়ার তুলনা!এইডা আইস্যকর😂😂😂,0,politics
রাজাকারের বিচার হইবে গলা শুখাই গেচে,0,politics
আমার হাতে কোন ঘড়ি নাই।!!!!,0,politics
দেশ এখন একনায়কতন্ত্র শাসন চলছে দুই টাকার কাজ শত টাকায় উন্নায়নের জোয়ার বয়ে গেছে যদি এমন ইনকাম কারো থাকে তার এমন শখ সাধারণ ব্যাপার,0,politics
চোর বেয়াদব খারাপ রাস্তা বাচ্ছা এগুলি আমাদের বাংলা গরিবে ভালো মানুষে প্রিয় নেতা জনাব ওবায়দুল কাদের সাহেব কে নিয়ে কাউয়া বলে এবন বাঁজে কতা বলে,0,politics
ফারহানা আপু সব লোকদের সাথে টক শো তে বসবেন না,0,politics
আমার একটা ফ্রেন্ড মাষ্টার্শ পাশ করে এখন একটা ফ্রিজের শো রুমে জব করে সেলারি মাত্র আট হাজার টাকা। কতো কস্ট করে পড়া লেখা করতে হয় আর পড়ালেখা শেষ হলে একটা চাকরি মেলাতে আরো বেশি কস্ট হয়।। আর এসব রক্ষক নামের ভক্ষকেরা দেশের মানুষের দায়িত্ব নিয়ে তাদের জীবন নিয়ে সাপলুডু খেলতেছে।।। আল্লাহ তাদের উচিৎ বিচার করবে।।,0,politics
ইটা উকিল মিড নাইট এমপি ভোট চোর তো শেখ হাসিনা । একটা বছরের শিশু ও জানে এই ভোট চোর হাসিনার ভোট চুরির কাহিনী। মিড নাইট ভোটে এমপি হওয়া যায় কিন্তু জনগণের সাপোর্ট পাওয়া যায় না। মিথ্যুক ধোকাবাজদের দল।,0,politics
দোয়া করি এগিয়ে যাও ভাই💚💙💛,0,politics
ধন্যবাদ।,0,politics
আমি কিছুই বলবো না সময় টিভিকে যে কমেনগুলো করছে মানুষ তা তুলে ধরলে হাসিনা সরকার লজ্জা আর কথা বলবে না হাসিনার উচিৎ এখন মরে যাওয়া ষ্টক করে,0,politics
হাগলে কি না কয় ছাগলে কি না খায়,0,politics
আমার নাম্বার সময় পাইলে কল দিয়েন,0,politics
তোর বাপের নাই কোন ঠিক। তাই এই সব কথা বলে বেড়াস,0,politics
রিজার্ভ চুরি করছে কি তোর বাপে,0,politics
সত্যি বলতে যেখানে আমরা বেকাররা হাজার টাকার চাকরির জন্য দৌড়াদৌড়ি করি। সেখানে দেশ চালাবে যে নেতারা তারই দুর্নীতি গ্রোস্থ। 😓😓,0,politics
বিশ্ব চোর আ তারা,0,politics
আমি কাওয়া কাদের বলছি এসব গুজব এসব কথায় কেও কান দিবেন না।।।,0,politics
জারজলীগ আর কি বলবো,0,politics
বাংলাদেশ এর উন্নয়ন। গুম ধর্ষন আর মানুষ খুন।,0,politics
কদু ভাই ভালো হবে না।,0,politics
প্রধানমন্ত্রীর সাথে আবার কি ভাবে মন্ত্রীর তুলনা হয় ? আমাদের জাতীয় ব্যাক্তিরা কি তাহলে মেধাহীন হয়ে যাচ্ছে। পাগলে ও ত জানে যে আমেরিকা বাংলাদেশের চাইতে ধনী।,0,politics
আঃলীগের মাথা সব নষ্ট হয়ে গেছে। অপু অকিল তো রুমিন ফারহানার সাথে কথা বলার যোগ্যতাই রাখেনা। সে আবার উবাইদুল কাদেরকে বেগম জিয়ার সাথে তুলনা করে। একটা পাগলেও তো এ কথা বিশ্বাস করবেনা। আসলে মাথা নষ্ট হয়ে গেলে কি বলে না বলে সে নিজেও বুঝেনা।,0,politics
সালা নাম্বার ওয়ান বাটপার,0,politics
ভাই অবাইদুল কাদের এটা আবার কে আমি প্রথম দেখলাম এই মানুষ টা ইন্ডিয়ানি নাকি বাংলাদেশি? তাও আবার এতগুলি মেয়ের মাজখানে হায় আল্লাহ এই বুডা বয়েসে এমন করলে আমরা কোথায় জাবো আমরা তো বিয়ে করতে পারবো না মেয়েরা বুডাদের পচন্দ করবে হায় হায় হায় আমি শেষ 🥶🥶🥶,0,politics
এক সরকার বার বার আসলেই দেশের জন্য বিপদ খন্তা দিয়ে খনন করা,0,politics
কাউয়া ডাকাত দলের সাধারণ সম্পাদক চোর সালা,0,politics
বাংলাদেশে শীষ প্রতিসঠান গুলো ভারত হাসিনার কৃতোদাশ,0,politics
হাচিনা তোরা সবাও চোর মানুষের টাকা লোড পাঢ করা খাচ আর বলচ দেশে নাকি কাজ করচ আরে কাজ করচ বাহিরের টাকা জনগনে টাকা তোরা খাচ,0,politics
ওবায়দুল কাদের কি জনগণের টাকায় বিলাসিতায় মেতেছে নাকি? কবে এসব এম পি মন্ত্রীরা জনগণের রক্ত চুষক শাসক না হয়ে জনগণের সেবক হবে কবে? জুতানোর পর নাকি জুতানোর আগে?,0,politics
চুদা জায়গা,0,politics
অনেকদিন পরে একটা ভালো কথা শুনলাম শুনে অনেক ভালো লাগলো এভাবে ভালো কথা বলবে আপনাকে লাইক কমেন্ট করে ধন্যবাদ জানাবো,0,politics
দুইটায় গান্ডু 😂,0,politics
খালেদাজিয়ার মুক্তি চাই,0,politics
বেঁচে থাকলে আরো এরকম ভিডিও দিস ভাই🙂,0,politics
এই সরকার চাই না,0,politics
সালায় নাটক করতে রাস্তায় আইচে,0,politics
সহমত !,0,politics
সরকার এসব দেখে না ৷৷৷৷ আর আমাদের দেশে তো সরকার নেই দেখবে কে ৷৷৷৷,0,politics
অপু উকিল বিয়াদব।,0,politics
অপু উকিল তুই একটা বেয়াদব মহিলা এবং মিত্থা বাদী,0,politics
কিজে বলব,0,politics
কাউয়ার সাথে মানুষের কেমনে কি ?? যাকে সবাই কাউয়া হিসেবে চিনে ।আর কথায় কথায় মিথ্যা বলে।। ছিঃ ছিঃ ছিঃ,0,politics
কাওয়ার থেকে বড় চোরকে আমদানি করবে,0,politics
ছারকে গারাইলে সব ঠিক হবে,0,politics
ডিম থেরাপি,0,politics
এগুলা তো অরিজিনাল নাও হতে পারে এখন তো সবকিছুর কপি পাওয়া যায় কম দামে।,0,politics
ইনু সাহেব মন্ত্রী হারানো বেদনায় কাতর।,0,politics
কাকূ আপনার গাড়ীর কাগজ পএ ঠিক আছে কিনা?,0,politics
আনডা আরও মারো,0,politics
কে বড় কে ছোট??এই গুলা নিয়া এত বাড়াবাড়ি করার কি আছে?,0,politics
আন্টি আপনি গিয়ে যান সাধারন মানুষ আছে আপনার সাথে জয় বিএনপির জয়,0,politics
চিন্তার খোরাক বটে,0,politics
ওবায়েদুলরা আসলে চারপোকা রক্ত খাওয়া ছাড়া আর কিছুই জানে না।,0,politics
পুরো দেশটাই এখন খাওয়া ভবন সামাজিক যোগাযোগমাধ্যমে বিভ্রান্তি ছড়ালে অপু উকিল নামককুলাঙ্গার এই অসৎ মিথ্যা বাদী জানুয়ারে বিচার করতে পারি।’ বড় মাপের চাপাবাজ ভবিষ্যৎ আওয়ামী চাপাবাজি লীগের সভাপতি করা হবে আরাফাত নামককুলাঙ্গার একজন মিথ্যা বাদি শয়তান,0,politics
পান থেকে চুন খসলেই বিএনপি কে দোষারপ করেন ওবায়দুল কাদের সাহেব অথচ নিজের হাতে শোভা পাচ্ছে লাখ টাকার ঘড়ি হাতে যদি লাখ টাকার ঘড়ি থাকে তাহলে অন্যান্য ব্যবহার্য সামগ্রীর দাম কত হতে পারে?? টয়লেটে কি তিনি ট্যিস্যু ব্যবহার করেন না হাজার টাকার নোট ব্যবহার করেন?? ইনকাম ট্যাক্সের ফাইলে কি এর উল্লেখ পাওয়া যাবে?? লজ্জা হওয়া উচিত আমাদের যে আমরা এমন রাজনীতিবিদের নেতা মনে করি। শুদ্ধি অভিযান শুধু চুনোপুটিদের ওপরে চালিত হয় এসব নেতাদেরও শুদ্ধি অভিযানের অাওতায় আনা উচিত।,0,politics
ভাই এসব বলে লাভ নাই। মানুষ সবই ভুলে যাবে।আপনার এই কথাগুলো দেখা পযন্তই। কিছুক্ষণ পর আবার ভুলে যাব।😞,0,politics
তোমার মত ইউটিবাররা লাইক কমেন্ট ভিউিয়ার পাওয়ার জন্য এসব ভিডিও বানাও কেন?,0,politics
টিক বলচে,0,politics
এই দালাল আবারও ইউটিউবে ?,0,politics
দুই লুটপাট দলের দালালি আর ভালো লাগে না।বন্ধ করেন এইসব দালালি,0,politics
পরিষ্কার ভাবে গাজা খোরের পরিচয় দিল,0,politics
ভাই আমরা বাংলাদেশের মানুষ বলদ কেন জান সরকারকে ভাল মনে করি তায়,0,politics
দেশে ভাল মানুষ একটাও রাখবেনা সালা ফেরাউনের বাচ্চারা দেশে থাকবে শুধু কুকুর জানোয়ারগুলো,0,politics
বছর আগে কাদেরকে শতকরা জনে ও ছিনতো না আর কিসে সাথে কি,0,politics
হে কুটনি রিজভী মাঝখানে ঢুকে কুটনামো করো?লাভ নেই লাভ নেই,0,politics
এটা হবে না আপনি ভুল লেখছেন,0,politics
মেও!! মেও!! ইনু ইবলিস,0,politics
বেগম জিয়ার অরিজিনাল জন্মদিন জানা গেলে বুঝা যাবে আসলে কে বড় 🙅,0,politics
হলুদ শাড়ি পরা মহিলার কথা হয়না মন গড়া কথা বলে মনে হল যেন ঝগড়া করছে এখানে পার্থক্যের কথা বলা হয়েছে যেখানে নিসন্দেহে খালেদাজিয়ার মর্যদা বেশী বেশী,0,politics
এইসব নাটক আর ভালো লাগে না,0,politics
বিএনপি সময়ে নাকি পাঁচ বার দুর্নীতিতে চ্যাম্পিয়ন হয়েছে আবার তাদের নেত্রীরা বড় গলায় কেমনে কথা বলে বুঝিনা,0,politics
সত্য সাহসী,0,politics
সব বিএনপির ষড়যন্ত্র।।।বিএনপির নেতারা এই ঘড়িগুলো ওনাকে করছে তাকে ফাঁসানোর জন্য।।🤣,0,politics
আলুর দোষ ঢাকতে না আলুর চাষ দেখতে ভালই বোলেছেন ভায়া।,0,politics
কার সাথে কার তুলোনা করে আর মানুষ পাইলো নাহ কাউয়ার সাথে ছি ছি ছি,0,politics
আপনি কাদেরকে এ সব কথা বলছেন?? আমরা হচ্ছি বাঙালি জাতি। যাদের চোখের সামনে দেশ বিক্রি হয়ে গেলেও নৌকা ধান দাড়িপাল্লা লাঙল বলে লাফাবে!!! যত দিন এরা থাকবে ততদিন এমন কাদের সাহেব হাজারো জন্ম নেবে আর আমরা চোখ বন্ধ করে বসে থাকবো। আপনি ভুলে গেছেন যে অন্ধ মানুষের শহরে আপনি আয়না বিক্রি করতে এসেছেন।।,0,politics
ইনুরে দৌড়ের ওপর রাখা খুবই ভালো।,0,politics
আল্লাই হেদায়েত দক কাদেরকে কাদের সাহেব আপনি তোওবা না করে মরিয়েন্না,0,politics
ওবায়দুল হক সাহেব আপনার সময়ও শেষ প্রযার্য় ইনু সাহেব এর মত আপনার ও হাওয়া একসময় শেষ হয়ে যাবে?,0,politics
আসসালামুয়ালিকুম ভাই আপনার উপস্থাপনা ও বচন ভঙ্গি মাশাআল্লাহ খুব সুন্দর লাগলো।,0,politics
কুতায় কাদের কাকু। কুতায় বেগম খালেদা জিয়া।হায়রে বাংলাদেশ ।কি আর বলব,0,politics
এটাই রাজনৈতিকের ধারা,0,politics
কাওয়া,0,politics
যে ভিডিও করছেন সে একজিন কামলা,0,politics
ভাই গিফট বলে একটা জিনিস আছে। নেতা খুব সৌখিন বড় কোন কাজে গেলে নেতাকে আর ও দামি ঘড়ি গিফট কইরেন।,0,politics
এই কামটা কিছু দিন আগে ছাত্ররা করে পেলছেতো। এখন এটা দেখানোর জন্য নাকি?,0,politics
আমার মামা পরে কোটি টাকা দামের ঘড়ি সে ব্যাবসা করে সখের বসে এত্তো দামি ঘড়ি কিনেছে তাহলে সে রাজনৈতিক ব্যক্তিত্ব বাংলাদেশের নম্বর ব্যাক্তি তাহলে সে লাখ টাকা দামের ঘড়ি পরে তাহলে তো কমি আরো দামি ঘড়ি পরা উচিৎ । কেন তোমার তারেক জিয়া যে বিলিয়ন ডলার বানাইছে ওইডাকি কুড়ায়ে পেয়েছে? চোর রা লাফাই বেসি নিজেই চুরি করে তো বিদেশে পালাইছিস।,0,politics
ওবায়দুল কাদের ও খালেদাএরা উভয়ই সিংগাপুর যাবে আর মাঝখানে সাধরণ মানুষ চিকিৎসা না নিয়েই মরবে !!!! বাঙ্গালী একজন কে সেবাই দেয়না আর কতজনকে একেবারে সিংগাপুর পাঠায়🤣🤣😅,0,politics
পুরাই হাস্যকর,0,politics
যতই লক্ষ টাকার ঘড়ি পড়ুক হাঁটে হিজরাদে র মতো কথা বলেন কাকের মতো কর্কশ ভাষা য়।ব্যাক্তি হিসেবে চাটুকার চরিত্র মনে হয় ।,0,politics
ইনু সাহেব একটু সবুর করুন। এখন শেখ হাসিনা ভালো ভাবে আপনাকে মূল্যায়ন করবেন। তিন টুকরা কাপড়ের চিন্তা করেন । বহুদিন বকবক করেছেন।,0,politics
এর হাতিয়ার গর্জে উঠো আরেকবার জিওয় ভুংগা ভুংগা,0,politics
এগিয়ে জান ভাই,0,politics
ভদৃ দেশে বলে ? আর তে রাস্তায় যাম লাগিয়ে করে অভদ্র ভাষা করে মন্ত্রী মঽদয় ।,0,politics
ভাই আপনি কি দেশে থাইকা ভিডিও বানান? আপনার জীবনের ঝুঁকি নাই? আমি তো আপনার অনেক ভিডিও দেখছি আর ভাবছি আপনার সাহস অনেক । সাবধানে থাকবেন ভাই । কারন বাংলাদেশে কি পরিস্থিতি তা আপনি ভালো করেই জানেন ।,0,politics
হুজুরকে নিয়া একটা ভিডিও চাই,0,politics
আজ ঈদ,0,politics
দীতিয় মেয়াদে জীবন দিয়েআছেন সৃষ্টিকর্তা লুটেপুটে খাওয়ার পর সবশেষে তারই নিকট ফিরে যাওয়া এবং হিসাব শুরু ।,0,politics
আমরা হাছিনার পতন চাই,0,politics
শান্তনু এত দিন পরে তোমার ভিডিও পেলাম তোমাকে অনেক ভালোবাসি সত্যের পথে আছো বলে।,0,politics
লোকগুলোর আর কাজ নেই? দেশে সাগর মহাসাগর চুরি হচ্ছে ওনারা আছেন ওবায়দুল কাদেরের ঘড়ি নিয়ে?,0,politics
বঙ্গবন্ধুর খুনিদের বিচারে আওতায় আনতে কমিশন ঘঠন করে সত্যিকার অর্থেই যারা দায়ী তাদের ফাঁসি চাই,0,politics
হে বাংলার সাহসী সেনাবাহিনীরা তোমরা কি এখনো ঘুমিয়ে থাকবে।তোমরা জাগো তোমরা জাগো।এক মাত্র তোমরাই পার আল্লাহর সহায়তা আমাদের বাংলাদেশ টাকে রক্ষা করতে।তোমরা কি ভুলে গেছো যে শপথ করেছিলে অন্যায়ের বিরুদ্ধে রুখে ধারাবে।যদি ভুলে না যাও তাহলে জাগ রক্ষা করো ঐ জালিমদের হাত থেকে।,0,politics
ওরে কে আছস আশেপাশে ওরে তারাতারি পাবনা নিয়া যা মন্ত্রীত্ব না পাইয়া পাগল হইয়া গেছে,0,politics
কে ভোট দিয়েছে জারজ সরকারের জারজ মন্ত্রি ও দেরতো কোনো অদিকার নাই এইগুলি দেখার,0,politics
আওয়ামীলীগ আর আওয়ালীগ নেই আওয়ান লীগ হয়ে গেছে,0,politics
অপু উকিলের কাত গুলার কোনু যুক্তি পেলামনা প্রশনের ঊত্তর দিতে না পেরে পুরনো বিসয় নিয়ে টাইম পাস করেছেন।,0,politics
মাথা কি গেছে নাকি কার সাথে কার কথা তুলনা করে কোথায় হল কাউয়া কা কা আর কোথায় বেগম খালেদা জিয়ার তোদের মাথা নষ্ট হয়ে গেছে,0,politics
এত টাকা দিয়ে কি আপনি বেহেশতে যাবেন? কাদের ভাই?,0,politics
ঢেলে দেন 😂,0,politics
এরকম শিক্ষককে জুতা দিয়ে মারতে হবে,0,politics
মন্ত্রীরা যদি সব সময় নায়ক নায়িকা নিয়ে পড়ে থাকে তাহলে এরা সাধারণ জনগনের সেবা কখন করবে,0,politics
খালেদা এইট পাস,0,politics
অনেক ভালো লাগলো স্যার।চোরের কিছু তথ্য জানতে পারলাম।আশা রাখি এই রকম আরো কিছু তথ্য পাবো ইনশাআল্লাহ।।।,0,politics
রুমিন ফারহান কে কঠিন ধোলাই দেয়া হয়েছে 😁,0,politics
কথাটা সঠিক,0,politics
কি কাউয়া,0,politics
কাওয়া না কুকু বলা চলে,0,politics
ভাই শেখ হাসিনা সন্তাস লালন পালন করে আমরা চাই শেখ হাসিনাকে মেরে ফেলুন,0,politics
মুসলিমদের দেশে হিন্দু নেত্রীত্ব মেনে নেওয়া যায়না।তারা আমাদের জাতির মধ্যে বিভেদ তৈরি করে বিশেষ সুবিধা ভোগ করছে।তারা ভারতের এজেন্ট।হিন্দুরা এদেশে ব্যবসা বানিজ্য করে ভারতে গাড়ি বাড়ি সহ অর্থ প্রাচার করছে।তাদের এদেশ থেকে তারিয়ে অতি তারাতারি ভারত পাঠানো হোক।,0,politics
ছাত্রলীগেএর সন্ত্রাশীদেরকে প্রতীহত করতেহবে।,0,politics
একটা কমেন্ট ও যদি ওনার প্রশংসা দেখতাম !! লোকটা আসলেই পাগল জনগণ যে ওনারে কাউয়া জানে এটা বোধ হয় উনি নিজেই জানে না😂😂😂,0,politics
অন্তত আওয়ামী লীগের প্রানের উৎসব শুরু হবে তখন,0,politics
শিক্ষক নামে লোকটাকে পিটানোর দরকার এদের কারণে আজকে বিশ্ববিদ্যালয়গুলোতে এই অবস্থা,0,politics
এত টাকা দিয়ে জান্নাতে যাবেন,0,politics
এই ভাইকে স্যালুট কল রেকট চেক করুন স্যারকে মিথ্যা বাদি প্রমান করুন,0,politics
সাংবাদিক ইলিয়াস ভাই একদম ঠিক কথাই বলে হালায় ঠোট মুখ কামড়িয়ে চিবিয়ে চিবিয়ে কথা বলে। শো আপ করে নিজেকে।একটা কথাও সালার মন থেকে আসে না সবই ইউ টিউবে কামাইয়ের ধান্ধা। এখনই চুপচাপ চ্যানেলটা আনসাবস্ক্রাইব করে চলে যাব। সালার মুখ যেন আজ জিবনে আমার না দেখতে হয়।,0,politics
খালেদা জিয়া হচছে বাংলাদেশের সবচেয়ে জনপ্রিয় একজন নেএী আমি বিএনপি করি না তবু ও এটাই হচছে বাস্তব সত্য কথা সত্য সুন্দর না হলে ও সত্য।,0,politics
তুমি আগামী নির্বাচনে মনোনয়ন পেলে স্বরাষ্ট্রমন্ত্রী,0,politics
ভাই দেশে বিচার নাই শেখ হাসিনা তোকে দিক্কার,0,politics
নামদিযা কি হবে দেশের মালিক যারা নামের কি কাম। ঝথসব দেশ আমার মাটি আমার জাতি আমার আমি হলাম সর্বহারা।। শ শ্শুর বাড়ি থাকি ঘর জামাই আমরা।।,0,politics
এরাই হলো জাহান্নামের লাকড়ি,0,politics
এভাবে করাটা ঠিক হয়নি কি বিচার দেশে,0,politics
ভাই তোরে কেউ কিছু কয় না ?,0,politics
এগুলাতো পোলাপানই করেগেছে ওকি বালফালাতে গেছেনা এটা ওর পোলা পানে শিক্ষাদিয়ে গেছে সেটা পালনকারী,0,politics
ভাই আও আমার বুকে আও,0,politics
রাস্তার ছেলে ওবাইদুল,0,politics
মহান আল্লাহ তায়ালার লানত হাসিনার সন্ত্রাস বাহিনীর উপর,0,politics
ছি ছি এগুলো মানুষ নাকি গুন্ডা,0,politics
এগুলো ত মেইড ইন গুলিস্তান ও হতে পারে।,0,politics
নিজের পকেট থেকে টাকা দিয়া দল চালাইছি কত নিজাতিএ হইছি সেই ফকরুলের আমলে বিদেশে পারি দিছি কারন দলে আমাদের যায়গা নাই এর কারন দলের এম পি মন্তীরা কারন রোদ বৃস্টিতে আরো কত কস্ট্র করেছি এই দলের জন্য আর এম পি মন্তীরা তারা তাদের বাতিজা বাইগনা ওমুক তমুক কিছুই করেনাই দলের জন্য তারাই এখন বড় বড় নেতা আর আমরা হইছি গলার কাটা আসলে এরই নাম সত্যি রাজনীতী ধন্যবাদ,0,politics
আওয়ামীলীগ মিথ্যাচার এটি সবাই জানে তবে এত বড জারজ মিথ্যাবাদী আজকে সচুকেক দেখলাম যদি বি এন পি সরকার দখল করে থাকে আমি বলব আপনার বাপ আপনার মাকে দখল করে জন্ম দিয়েছে নাকি? যদি তাই হয়ে থাকে তাহলে তো আপনি জারজ সন্তান বাংলাদেশের ইতিহাসে সালের মত পিয়ার ইলেকসন হয়নাই আর আপনি বলতেছেন কী? ??কি আর বলব আওয়ামীলীগ এখন দিশা হারিয়ে পাগল লীগে উপাধি লাভ করেছে তাই আমি বলি দেশের মানুষ আজ এত পাগল নয় যে পাগলের সাথে কথা বলতে যাবে।,0,politics
চুরির টাকায় কিনা,0,politics
আপনার ভিডিও টি খুব ভালো লেগেছে।।।এবং অনেক গুরুত্বপূর্ণ একটা তথ্য জানতে পারলাম।।।,0,politics
ইনু এখন মাইনকার চিপায়।,0,politics
এই সব বুড়া ধুড়া ডেট ফেল এমপি মন্ত্রী না থাকাই ভালো চোড়ের দল সব আবার নতুন করে নতুন দের কে চুড়ি করার সুযোগ দেয়া হোক বাংলাদেশের রাজনীতি নোংড়া,0,politics
লানত তোদের উপর ধ্বংস হ তোরা,0,politics
চুরেরা চুরি করে আর সাদারন মানুষ এর মাসুল দিতে হয়,0,politics
আকাশ ভরা তারা কাকু তোমার গোয়া ম্রা সারা😂 এখন পাম্প দিতাছে আর একি কথা বারবারি বলতাছে😂,0,politics
সব শোভনের চক্রান্ত? সুন্দর গাধা ভিপি হতে পারে নাই এই কস্ট সহ্য করতে পারছে না বলে ঢাকা বিশ্ববিদ্যালয় রনক্ষেত্রে পরিণত করছে?,0,politics
বাংলাদেশের সেরা সাহসী ইউটিউব আপনি। এগিয়ে যান ভাই দোয়া করি😍😍😍😍😍😍😍😍😍😍😍😍😍😍😍😍😍😍😍😍😍😍😍🖐🖐,0,politics
সব যুবকদের নেতৃত্য চাই।,0,politics
রুমিন আপু❤❤,0,politics
গরিবদের অর্থ হাতিয়ে নিচ্ছে এই কুত্তার বাচ্চা👈,0,politics
সা,0,politics
আওয়ামীলীগ এর কাছ থেকে ভাল কিছুর আশা করা যায়না,0,politics
সারাজীবন আওয়ামী লীগ করেছি। অথচ এখন ঘৃনায় ভাষা হারিয়ে ফেলি।ছি তোরা আবার দেশ সাধীন করেছিস বলে দাবী করিস। বেহায়া নিরলজ্জ,0,politics
আমাদের মাননীয় প্রধানমন্ত্রীর কাছে বলবো ইনু একটা কালপিট,0,politics
ফারহানা আপু এগিয়ে যাও আগামি দিনে,0,politics
শিক্ষা ব্যবস্থা কে দংশের পথে ঠেলে দিচ্ছে আওয়ামী সরকার,0,politics
এগুলো আমার টাকায় কিনা না 🐸🐸 এগুলো আমাকে গিফট করছে🐸🐸 শুনে আমি শিহরিত 🐧🐧,0,politics
ওমা ঘড়ি পরলেও দোষ ৷ উনি মারাক্তক রকমের সৎ ও নিবেদিত প্রানের মানুষ ৷ সবাই বলে তো ৷,0,politics
ভাই আপনার ভিডিওগুলো আমার কাছে খুব ভালো লাগে অন্ধকারে চাপা পড়া সত্য গুলি আপনি সব সময় তুলে ধরেন আপনাকে অনেক ধন্যবাদ এই কারণে কারণ এখন মানুষ সত্য বলতে ভুলে গেছে,0,politics
ওবায়দুল কাদের সাহেব কে বাঁজে কতা বল্লে সে জারজ সন্তান,0,politics
দুই জনকে ফিতা দিয়া মাপ নিলে বুঝা যাবে কে বড়?,0,politics
পাগলের প্রলাপন হাস্যকর বটে!!,0,politics
ওবায়দুল কাদের কাউয়া কাদিরা ও তো কথায় নোলতে পারেনা কায় কায় করে তিন বারের নেএীর সাথে মিলায়তেছে,0,politics
হায়রে ঢাকা বিশ্ববিদ্যালয়!!!,0,politics
আমাদের অনেক খারাপ লাগে আমাদের আর উঠে যাওয়ার পরে,0,politics
ঠিকেই নেতা,0,politics
ছাত্রলীগ আর ছাত্রলীগ নেই ওরা মানুষ নামে জাতীর কলঙ্ক,0,politics
ওবায়দুল কাদেরকে। খালেদার জিয়া জুতা পাহারাদার রাখবে নি,0,politics
মাটির ভিতর তো যেতে হবে মুনকার ও নাকির অপেক্ষা করছে,0,politics
আলুর দোষ ঢাকতে এবং চাষ করা শিখতে বিদেশী নটীদের কাছে ধরনা এবং আনন্দভ্রমণে যাচ্ছেন কুলা গুলা।,0,politics
আস্তাখফিরুল্লা আল্লাহ কে বয় কর,0,politics
ভাই আপনার জন্য শুভকামনা রইল।। 💚,0,politics
ভাই সাবাস চালিয়ে যান হয় তো কোন এক দিন আপনার কথা কাজে আসবে আমি আপনাকে বংগবীর বললাম,0,politics
এই যদি হয় প্রাচ্যের অক্সফোর্ডোর অবস্থা? এরা মানুষ? এরা ছাত্র-ছাত্রী? এটা কি সত্যিই দেশ খ্যাত ঢাকা বিশ্ববিদ্যালয়? ধিক্কার জানাই ছিঃ ছিঃ ছিঃ,0,politics
বাংলাদেশের থিকে ছাএলিক বাদ দেয়া হক,0,politics
আমি কেমরা মেনদের অনোরত করে বলবো আপনারা এই বাটপারে পিছুনে এই দালালের পিছুনে পা চাটা কাদের পিছুনে না হেটে।।। ভাল মানুষের পাসে দারান তাহলে মহান আল্লাহ আপনাদের পাসে দারাবে,0,politics
অস্তির ভিডিও অনেক ভাল লাগলো,0,politics
সুদ্ধি অভিজান চালাবেন না ওবায়দুল সাহেব,0,politics
ওয়াও অসাধারণ কার সাথে কার তোলনা,0,politics
যুদি মোবাইলেই কতা বলতো খাদের তাহলে আমার মনে হয় সবয়েয়ে বেশি টেক্চ আসতো খাদেরেই কতা বলতে ও এখনো শিকেনায় নোযাখাল্লা,0,politics
ওবায়দুল কাদের যেই পরিমাণ ফুটেজ খায় তামাশা কইরা এই সময়ে কয়েকশো মুভি দেখানো যাইতো।,0,politics
ভাই আপনি নিয়মিত ভিডিও আপলোড করেন না কেন? নইলে এতদিনে প্রায় মিলিয়ন সাবস্ক্রাইবার হয়ে যেত,0,politics
ভাই আপনি সুবিধাবাদ লোক,0,politics
ভাই আমাদের দেশে যে রকম টাকার কুমির আছে বিলাসী অনেক লোক আছে আবার রাস্তার ধারের ফকির আছে সেটা ভিন্ন কথা তবে আপনাকে দেখি আমেরিকাতে থাকেন প্রায় বাংলাদেশের অনেক কিছু নিয়ে ভিডিও বানান এগুলো কমবেশি আমরা সবাই জানি আপনি আমেরিকায় আছেন সেখানেই কিছু নিয়ে ভিডিও বানান আমরা দেখি শুনি এবং জানি ?,0,politics
আরে ভাই নিজের দিন না বদলে কি আর অন্যের দিন বদলানো যায়!!!!!,0,politics
আপনাকে ধন্যবাদ স্যালুট জানাই আন্তরিক শুভেচ্ছা ও অভিনন্দন জানাই,0,politics
ঠিক আছে। আগের জারা ওরা তো পেঠ ভরে ব্যাংক ভরে সব ভরে পেলেছে। এখন ওদের নিচের পদে জারা তাদের পেট ভরাতে হবে। নয় সরকারের ওয়াদা ঠিক থাকবেনা। সরকার পদ হারাতে হবে। তাই নতুন কিছু আইন করা হচ্ছে।,0,politics
ধন্যবাদ ভাই😇❤ ভালবাসা রইল 😘❤,0,politics
এটা কোন ধরনের আইন,0,politics
মন্ত্রী সাহেব যতগুলা গাড়ি চেক করলেন। একটা গাড়ি চালকেরও সিটবেল লাগানো নেই। কি যে চেক করল কিছুই বুঝলামনা। কিন্তু মনে হচ্ছে কোন সিনেমার সুটিং চলছে। বাহিরের দেশগুলোতে ট্রাফিক আইন গুলো অনেক কঠিন হয়। আমি সৌদি আরবে গাড়ি চালাই। এখান কার নিয়ম কানোন সঠিক ভাবে মেনে গাড়ি চালাতে হয়।।,0,politics
কি সুন্দর লেখা পড়া,0,politics
এদের কুকুর বললে কুকুরও লজ্জা পাবে,0,politics
রুমিন ফারহানা আপু সত্য কথা বলেছেন।❤,0,politics
সাবাস সাংবাদিক,0,politics
অনেক ইচ্ছে নিয়ে দেশের নাগরিক হয়েছিলাম কিন্তু আজও দেশের নাগরিক হিসেবে ভোট দিতে পারিনি আর কখনো পারবো কিনা তাও জানি না,0,politics
আওয়ামী পাগল,0,politics
এখন কাদের বলবে এটা গুলিস্তান এর ফুটপাত থেকে কেনা এটা আসল নয়।,0,politics
সাধারণ সম্পাদক হিসেবে সৈয়দ আশরাফ ই বেস্ট।,0,politics
বিয়াদব হওয়ার জন্য মুর্খ হতে হয়না ছাত্রলীগ হলেই যথেস্ট ।,0,politics
নিয়মিত হয়েছেন ভাল লাগছে । আশা করছি এখন হতে নিয়মিত আলোচনা করবেন ।,0,politics
মুক্তী চাই বেগম জিয়ার মুক্তী চাই ং,0,politics
হাসবো নাকি কাদবো বুঝতে পারছিনা কোথায় বেগম খালেদা জিয়া আর কোথায় ওবায়দুল কাদের হহহহহহাা,0,politics
তুই মনে হই কাদেরিয়ার দালাল? মিথ্থা কথা বলচ কিল্লাই ??,0,politics
এটা ছাত্র লীগের কোন ধরনের ব্যাবহর,0,politics
তা ছিল প্রয়োজনে সবাই রাজাকার শুধু অাপনি মুক্তি,0,politics
ভি পি সত মানুস তার পাশে সারা বাংলাদেশের মানুস আছে,0,politics
বিএনপি জামাত এর সরযন্রের জালে ফাইসা গেছে কাদের 😆😆😃,0,politics
অপু উকিল একটা পাগল।কোথায় দেশের প্রধানমন্ত্রী ছিলেন খালেদা জিয়া।আর কোথায় কাওয়া কাদের সরকমন্ত্রী।ভোট চুরের দল আওয়ামিলীগ।,0,politics
এটাই বাংলাদেশ।,0,politics
দুঃখ হয় এসব দেখে যারা আদেশ দেন তাদেরই মাঠে নামতেে হয় কারণ কেউ কারো কথাই শুনেনা কালা দেইখা ও দেখেনা কানা।,0,politics
এইসব পাগল ছাগল টিভির পর্দায় আসে কোথার থেকে,0,politics
কিছু মানুষের খাইয়া কাজ নাই এমনি এক জিনিস নিয়ে মাথা নষ্ট করে।,0,politics
ভাল দেশ উন্নতি হচ্ছে।,0,politics
শেখ হাসিনা অত্যন্ত বিচক্ষণতার পরিচয় দিয়েছেন আপনার মত একজন অবিশ্বাস্য নিরব বিশ্বাস ঘাতক কে ছুড়ে ফেলেছে কারণ যে ব্যক্তি স্বার্থের জন্য অন্য নেত্রী কে কটাক্ষ করে ও গালিগালাজ করে কথা বলে তার কাছে কতটা নিরাপদ প্রধানমন্ত্রী যে কিনা বঙ্গবন্ধুর স্ববিরোধী,0,politics
আপনার চ্যানেল ব্যান করা হোক আপনি কাউয়া কাক্কু রে নিয়ে ট্রল করছেন আপনি জামাত,0,politics
যোগ্য নেতা ওবাদুল কাদের কারন সে নিজের যােগ্যতা এখানে এসেছে আর খা্লেদা এসেছে মিরজাফর মােস্তাকের হাত ধরে।,0,politics
বালের ওবায়দুল কাদের বালের ঘড়ি।ক্ষমতা শেষ হয়ে গেলে সব শেষ।,0,politics
হিংসা লাগে,0,politics
চশমা ওয়ালার বাল জালায় নাই। কুকুরের বাচ্চা কথাটা কি বল্ল ।নিবাচিত এক জন ভিপি সে যে কোন সময় ভাল-মন্দে জন্য উপস্হিত হতে পারেন।যে বাযারা তার উপর হামলা চালিয়ে ছিল জরুরি তাদের গ্রেপতার করার জন্য ছাএ সমাজ কে বলছি।বতমানে দেশে সরকার আছে কি না জানি না।,0,politics
বিএমপি ঝখন খমতায় ছিল থকন এই ওবায়দুল কাদের বলেচিল আগুন জলচে জলবে শেই ওবায়দুল কাদের মুকে মুকে মিতাবাদী,0,politics
এস এস সি পাশ আর এর থেকে বেশি পডাসোনা পাশ।আপনারাই বিবেচনা করুন কে যুগ্যতা বেশি।,0,politics
আমরা পরিবর্তনগুলো দেখতে পাইনা। শুধু চোর খুজে বেড়াই। আওয়ামীলীগ চোরে ভরে গেছে ডাকাতে ভরে গেছে সত্য তবে দেশের অভূতপুর্ব পরিবর্তন এসেছে একথাটি আরও সত্য। সে আলোকেই সৃষ্টিশীল সমালোচনা হওয়া উচিত। আমাদের মন্তব্যগুলো দেশে বিলুপ্ত প্রায় টোকাইদের মত।,0,politics
ফাটাকেষ্ট পুরা,0,politics
আমিতো ভয়ে আছি রেল মন্ত্রীর মতো বিয়ের প্রস্তাব যদি দিয়ে ফেলে। সত্যি করে বলোতো কা কা তেঁতুলের মতো জিবে জল আসে কিনা ? আমিতো মনে করি আল্লামা শফি হুজুরের কথাই সত্যি। যদি ও গাধারা স্বীকার করে না।,0,politics
বাংলাদেশের ছাএ সমাজ +সর্বপরী জনগোষ্ঠী ভিপি নূরের সাথে সহমত পুষুন করে আগামী দিনের শিক্ষা ব্যবস্থা সঠিক পথে চলে যেনো কোন শিক্ষাপতিষ্টানে কোন মায়ের বুক খালি না হয় +দেশের অপশক্তি কে দমন করো,0,politics
হাতুরী লীগ থেকে ডিম লীগ সাবাস এগিয়ে যাও,0,politics
সময় ভালো তাই কোটি টাকার ঘড়ি পরে সময় খারাপ হলে ঘড়ি থাকবে না,0,politics
অপু তুই জানিস না বেগম খালেদা জিয়া কি।।,0,politics
জনগনে টাকা দিয়ে তারা করে।,0,politics
আপনার মত আপনি এগিয়ে যান আমরা পাশে আছি।,0,politics
কাউয়া ঢুকছে 😀কাউয়া দিয়ে কাউয়া তাড়াতে হবে ।। ধন্যবাদ ভাইজান আপনাকে এমন কনটেন্ট সবাই তৈরি করতে পারবেনা সাহসিকতার পরিচয় দিয়েছেন । আমাদের দেশের একজন ইউটিউবার রোষ্ট ভিডিও বানায় ও কোথায় এখন কাদের কে নিয়ে রোষ্ট কোথায় ।।,0,politics
এগুলো জামায়াত বিএনপি র গভীর ষড়যন্ত্র,0,politics
এক জনের বাপ আরেক জনের স্বামী এটা নিয়ে তো আমাদের দেশ শুধু তাদের ইতিহাস?,0,politics
বিনপি জামাতের ষড়যন্ত্র সব।এগুলা ফুটফাতে টাকাই পাওয়া যাই।😂😂😂,0,politics
ধন্যবাদ আপনাকে,0,politics
লীগমুকতৃ শিক্ষাজ্ঞন চাই।,0,politics
এই দেশের মহিলারা এত খারাপ যে।তাদের কে কোন দিন আর ঘরে ফিড়ানো যাবে না,0,politics
আওয়ামী লীগ এমন একটা দল তারা মনে করে দেশের মানুষ তারা কিছুই জানেনা কিছুই শুনে না তারা মনে করে দেশে যত শিক্ষিত আছে সবাই আওয়ামী লীগ । আরে একটা মানুষ যদি জীবনে কিছুই না বুঝে আওয়ামী লীগ ভোট ডাকাতি করে এটা ত দেখা। অপু আপু সবায় আপনাকে ভালবেসে অনেক কিছু বলেছে। সরম থাকে যদি মনে হয় মানুষকে এই মুখ দেখবেন না।,0,politics
ঐ মহিলা টাকে সব কমেন্ট গুলো দেখানো হক মানুষ কি বলে,0,politics
এত টাকার মালিক সে সরকারি বেতন পাই কত সব চুর,0,politics
এটার বিচার চাই,0,politics
সব তামসা করে,0,politics
যারা এই দরনের করমো কানডো করে তাদেরকে দিবালোকে জুতা পিটা করে পাঁয়ি দেয়,0,politics
সত্যের পথে থাকলে ভাই কিছু বৃথা দিতে হয়।এগিয়া যান ভাই দোয়া রইল।,0,politics
ভাই একটু সাবধানে থাইকেন,0,politics
দূর্নীতির বিরোদ্ধে অলোচনা অব্যাহত থাকুক। তবে এটাও সত্য যে পূজিবাদী অর্থনীতিতে দূর্নীতি না থাকলে নাকি অর্থনীতি চলে না।,0,politics
ভিপি নুর ভাই তােমাকে অনেক ধন্যবাদ কারন তুমি সত্যি কথা বলে ভাই তুমি শাবদান নে থেকো,0,politics
কাউয়া কে কাউয়া বলা অত্যন্ত সমুচিত।,0,politics
ভাই এরে কেউ চোখটা মুছে দে,0,politics
ওবায়েদুল কাদের হলো এম এ পাস আর খালেদা হলো এইট পাস তে কি তুলনা হবে,0,politics
এটাকি মন্ত্রির কাজ পালতু কুতাকার,0,politics
তুমি তো মেম্বার ও হতে পারবা না নৌকা বাদে,0,politics
অপুকে মদ খায়ানু হক,0,politics
বাংলাদেশ চলচ্চিত্র টা হয়েছে একটা ভদ্র পতিতালয়,0,politics
উপউকিল টোটালি পাগল,0,politics
বাংলাদেশের এক তৃতীয়াংশ মানুষ তিন বেলা ঠিক মত ভাত খেতে পারে না! এরা কোথায় আছে? কই থাকে?,0,politics
ওবায়দুল কাদের লোক একটা হাইস্যকর,0,politics
কি অবান্তর কথা বলার কারনে এ ধরনের কথাই সত্য।,0,politics
ভাই কোথাই আগর তলা আর কোথাই চকির তলা,0,politics
কোন একদিন সময় আসবে পানি খাওয়ার সময় পাবিনা।সময় থাকতে ভাল হয়ে যা,0,politics
জন্য পুলিশই যথেষ্ট। ম্যাজিস্ট্রেট লাগে না। এরজন্য দরকার সততা।,0,politics
এতিমের টাকা চোর খালেদা চোরকে পাকিস্তান পাঠিয়ে দিন,0,politics
একে জে মারলো আমার বালো লাগছে,0,politics
ভাই মজনু কে নিয়া একটা ভিডিও বানান,0,politics
অপু উকিল বড় নাকি সুইপার বড় ?,0,politics
কাউয়া হাদেরর তুলুনা জুতার সাথেও হয় না,0,politics
দারুন।,0,politics
এখন আপনার চ্যানেলটি বন্ধ হয়ে যায় কিনা এটাই দেখার বিষয়।,0,politics
আমি কোন দল বুঝিনা। আসলে যারা বেগম জিয়া কে কাদেরের সাথে তুলণা করে তাঁরা সম্ভাবত মানুষিক রোগী। আপনার হয়তো বেগম জিয়াকে ভালো নাও লাগতে পারে তাই বলে কি বাস্তবতা ভুলে যাবেন??,0,politics
কারোকে কথা বলার সুযোগ এ দেয় না,0,politics
যান যাট করে এ কেমন লাইসেন্ছ চেক করা বলে ভাই ওবাইদুল কাদেরের ভয় লাগে যদি জামাত শিবির আসে এজন্য আস পাসে লোক রাখছে,0,politics
হায়রে বাংলাদেশ,0,politics
ঠিক ভলেচেন,0,politics
লক্ষ লক্ষ টাকা দামের জামা কাপড় ঘড়ী পরতেছেন আপনি। তবে এটা মনে রাখবেন যে মৃত্যুর সময় টা সাদা কাপড় সাথে করে নিয়ে যেতে। আল্লাহ আমাদের সবাই কে সঠিক পথে হালার রুজি উপার্জন করার তৌফিক দান করুন আমিন।,0,politics
তুমি সাহসী ভাই,0,politics
বেকবকিনা অন্য লোক আসে তোমারা নিয়ে যা তোমাদের দল ছলার লোককিনেই তাহালে বিএনপি তোমাদের দল ছলাল,0,politics
একজন সাধারণ সরক মন্ত্রী কিভাবে একজন বেগম জিয়ার তুলনা করে।,0,politics
নুরু ভাই আমরা আছি আপনার সাথে৷৷ আপনার কিছু হলে সারা বাংলাদেশের মানুষ রুখে দাঁড়াবে,0,politics
বাংলাদেশের আরেক নাম খালেদাজিয়া 😂😂😁😁,0,politics
চোর চুরি করে ধরা খেলে তাকেতো শাস্তি পেতেই হয় !! খালেদাজিয়া ও তারেক কোকো মা ও ছেলে সকলে দেশটাকে ধ্বংস করে বড় বড় কথা বলে তারা নাকি চোর না !!!,0,politics
তুমি এত দিন পরপর ভিডিও দেও কেনো সান্তনু ভাই,0,politics
ওবায়দুল কাদের এর কোনো ছেলে মেয়ে নেই।তাই এবাবেই সে টাকা খরচ করছে।,0,politics
বেয়াদব খালেদা মরলে কিছু আসে জায়না,0,politics
ঢাকা বিশ্ববিদ্যালয় এ কি পড়া লেখা হয় নাকি এসব ই হয়?,0,politics
কাদের ত কাক!কালো কাক ইদুরের চেয়ে নিকৃষ্ট!!,0,politics
ওবায়দুল কাউয়া বড় কারন ও হাসু অাপুর ওইটা,0,politics
খালেদা তো মুরগির উপরও বোম মারছে😂😂🤣🤣😛😛,0,politics
ডান্ডি কয় কি,0,politics
কাতি বাই সব মানুয বোজেগেচে,0,politics
ধিক্কার জানাই এইসব অসৎ রাজনীতিবিদের,0,politics
নুরবাই আপনাকে আললা হেবাজত করবেন আপনি সতপতে থাকুন আপনার কোন বয়নাই আললা আপনার সাথেআছে,0,politics
অনেক বড় ভুল করবে আওয়ামী লীগ সরকার কাদেরকে সরিয়ে দিলে।,0,politics
আপনাদের নিউজের তারেক দিচ্ছেন না কেন,0,politics
শুধু গাড়ির লাইসেন্স নয় হাসিনার দেশ চালাবার লাইসেন্স আছে কি? অবৈধ গাড়ির ন্যায় হাসিনাও অবৈধ। ভারত ও আইন শৃংখলা রক্ষাকারী বাহিনি উপর ভর করে ছাড়া তার চলার উপায় নেই। কার্যত সারা বিশ্বের মানুষ জানুয়ারির নির্বাচন এবং তার পরে গঠিত সরকারকে অবৈধ বলেই বিবেচনা করছে। শুধু ভারত ছাড়া। এ ব্যাপার ভোটারবিহীন নির্বাচন ও অবৈধ সরকার গঠন ঘটেছে দিল্লির সরকারের উত্সাহ ও প্রত্যক্ষ হস্তক্ষেপের ফলে। এই পৃষ্ঠপোষকতা ছাড়া সারা বিশ্বকে বৃদ্ধাঙ্গুলি দেখানোর সাহস হাসিনা ও আওয়ামী লীগের হতো না। রাষ্ট্রীয় বাহিনীগুলোকে অবৈধ ক্ষমতা রক্ষার পাহারাদার বা লাঠিয়াল হিসেবে অপব্যবহারের উদ্দেশ্যে ক্ষমতাসীনেরা আইন প্রয়োগকারী সংস্থাগুলোর নিয়ন্ত্রণের ভার দলবাজ বিতর্কিত স্বার্থান্বেষী ও সুবিধাভোগী কিছু কর্মকর্তার হাতে তুলে দিয়েছে। রাষ্ট্রের সর্বত্র মেরামত দরকার আর তা হাসিনাকে দিয়েই শুরু করতে হবে।,0,politics
বাংলার বুকে যত আওয়ামিলিগ আছে সব এক সাথে করলেও বেগম জিয়ার একটি পসমের সমান হবে না,0,politics
ঘড়ি মার্কায় ভোট চাই,0,politics
বিচার যখন থাকে না সমস্যার সমাধানও হয় না। সব সমস্যা বরং পুঞ্জীভূত হয় আরও। আমাদেরও তাই হচ্ছে।😭😭😭 হায়রে বাংলাদেশ 😒😒,0,politics
খানকির পোলা,0,politics
দুই নৌকায় পা দিয়ে বাচতে চায় আওমালিগ,0,politics
এ সব আহামরি কিছু না। ইউনিয়ন পরিষদের চেয়ারম্যান ও গাড়ি চালায়,0,politics
ভালো কাজ করতে গেলে বাধা সামনে আসবেই।নুরু ভাই এগিয়ে যাও।,0,politics
অপু শালিকে টকশোতে দেখতে চায় না আমরা,0,politics
সাগর রুনির মত সাংবাদিক দম্পতি হত্যার ব্যাপার এ জাতী ভুলে গেছে অন্য সব হত্যার ঘটনাতো ধামাচাপা পড়া অতি সাধারণ ব্যাপার। এ জাতি বড়োই ভুলোমনা😢😰😰😢,0,politics
বিএনপি,0,politics
রাইট কথাটা বলছেন আপু মিডিয়া গুলো মিথ্যা প্রচার করে,0,politics
সব শালারাই ত চোর এখানে কাকে বাদ দিয়ে কাকে রাখবে কথায় আছে চোরে চোরে মামাত ভাই,0,politics
ভালোবাসি ভালোবাসা চলমান,0,politics
অপেক্ষার পর পাইলাম ভাইয়া আপ্নার ভিডিও অস্থির হইছে ভাই 👌👌👌,0,politics
একজন মধ্যবিত্ত ঘরের সন্তান হিসেবে আমি বলতে পারে বাংলাদেশে জীবিকা রক্ষা করার জন্য কত কষ্ট করতে হয়,0,politics
মিথ্যা কথা বলা মহাপাপ,0,politics
নূর ভাই আমরা পাশে আছি,0,politics
আমি মনেকরি এই মুহূর্তে জয় ভাইয়াকে দলের প্রধান সভাপতি করে প্রধানমন্ত্রীকে দলের উপদেষ্টা করলে দলের ওদেশের জন্য ভালো হবে।,0,politics
তুই আসলেই একটা মাল,0,politics
বিএনপি র জামাতের মত দল জদি শূন্য নেমে আসে তাহলে আমিলিগ চাইলে জাসদের পতিক মার্কা নেতা কিছুই খুজে পাওয়া য়াবে না এবং আমিলীগ এর নৌকায় উঠে অনেকটা পথ এসেছো আর নয় তোমরা য়ে সেক মজিবারের হত্যাকারি আমিলীগ তা জেনে গেছে তাই সেক হাচিনা মন্তী সবাই তোমাকে ফেলে দিলো আর জতোনা লাফালাফি কর কুনো লাভ নাই তবে সামনে আর কোন জাসদ মন্ত্রী হবে না আগামীতে পারলামেন্ট মেম্বারও হবেনা সংসদে পদ জদি হারিয়ে জাই তাহলে আর নতুন করে আর গ্রামেগন্জে মিটিংহবে না আর কোনো জাসদের কর্মী সদস্য কিছুদিন থাকবে না আমার মনে হয় হয়তো এটাই সত্য হতে জাচ্ছে,0,politics
বাংলাদেশের আরেক নাম খালেদা জিয়া,0,politics
আশা করি এভাবে যৌক্তিক সমালোচনা বৃদ্ধি পেলে রাজনীতিবিদরা আরো সতর্ক হবে অসৎ মানুষ রাজনীতিতে আসতে ভয় পাবে,0,politics
তোর পেট ভরে গেছে,0,politics
তুমি কে,0,politics
ফাটিয়ে দিয়েছ গুরু😍😍😍,0,politics
জিনিস একটা শেখ হাসিনা পুতুল যাতে প্রধানমন্ত্রীত্ব পায় সেই পথটা পুরাই পরিষ্কার করবে,0,politics
এতো চোরের চোর এই চোর কোথেকে যে পয়দা হয় জানি না। পাকপাকিস্তানিরা টাকা পয়সা সব নিয়ে গেছে চোর গুলা থুইয়া গেছে চোর কয়ড়া নিয়া গেলে বাঁচতাম বঙ্গবন্ধু নিজে যখন এই কথা গুলা বলছে স্বাধীনতার পর তখন কম দুঃখে বলে নাই,0,politics
স্যার ওনি হলেন ঘড়ি মানব,0,politics
আম্মা লিগ🤣🤣,0,politics
পাক্কা পিলিয়ার।,0,politics
দেশের পুটকি মারা শেষ।,0,politics
এই সার ও দলবাজ এটা বোঝতে আর ভোল নেই।,0,politics
কাওয়া আর কা কা করবে না😁😁😁,0,politics
এক্টা ঘড়ির দাম লক্ষটাকা পর্যন্ত এই কাওয়া কাদের পরে,0,politics
শালারা জনগণের টাকা মেরে ভোগ বিলাসিতা করে আর গরিবরা না খেয়ে মরে এই হলো বাংলাদেশের রাজনীতি,0,politics
অপু উকিলের কথা শুনে মনে হয় আওয়ামিলীগ বেধ ভাবে খমতা আছে মিথ্যা কথা বললে দলের ভালো হবে কিন্তু আপনার পরকালে কি হবে জানেন,0,politics
কা কা কাকুর আকরম পাস,0,politics
জ্যাম লাগাইয়া লাইসেন্স চেক মাথায় কি সমস্যা এদের ।,0,politics
কোন দেশে আমরা বাস করি যে দেশে একজন বিপির নিরাপত্তা নাই সাধারণ মানুষের নিরাপত্তা কিভাবে দিবে,0,politics
বর্তমান আওয়ামী লীগের জন্মদাতা হলেন শহীদ রাষ্ট্রপতি জিয়াউর রহমান জনাব শেখ মুজিব স্বাধীনতায় নেতৃত্বদানকারী দল আওয়ামী লীগ বিলুপ্ত করে বাকশাল গঠন করার পর সালে দেশের দ্বিতীয় সংসদ নির্বাচনের সময় তৎকালীন আওয়ামী লীগ নেতা মরহুম জনাব আব্দুল মালেক উকিল জিয়াউর রহমানের কাছ থেকে আওয়ামীলীগের সনদ গ্রহণ করেন আওয়ামী লীগের গুলিস্তানের বর্তমান প্রধান কার্যালয়টি ও জিয়াউর রহমানের অবদান এ প্রাপ্ত সত্য হারালে জাতি মিথ্যার উপর বসবাস করবে আমরা স্বাধীন জাতি এবং মুসলিম তাই সত্যি হোক আমাদের একমাত্র ব্রত রাজনীতির নামে অসত্যের রাজনীতি কাম্য নয়,0,politics
এখানে ভারতের দালাল,0,politics
দুই তিন জন দিয়া শাক দিয়া মাছ ডাকা যাবেনা এত হাজার হাজার কোটি টাকা পাচার করে ওদের কি হবে,0,politics
সড়ক মন্ত্রীর গালে জুতা চোরের ঘরের চোর চুরি করে নির্বাচন সুস্থ নির্বাচন হলে আওয়ামী লীগএকটা ভোট পাবে না,0,politics
কাউয়া শালায় বর লুচা,0,politics
আওয়ামীলীগ সংগঠন কি হাসিনার বাপে প্রতিষ্ঠা করছে নাকি স্বৈরাচারী হাসিনা ছাড়া বিকল্প কেউ নাই,0,politics
ভালো তো,0,politics
এগিয়ে যান জনগণ এদেশের বোকা,0,politics
বানোয়াট কথা বার্তা,0,politics
ভাই আপনার মতো যেই সত্য কথা বলেছে সে ই বিপদে পড়েছে দোয়া করি ভাল থাকবেন।,0,politics
অপু যে একটা আওয়ামীলীগ সেটা কথাতেই বুঝা যায়। ওরাতো মানুষ না।,0,politics
যেদিন শেখ হাসিনা সভাপতি পদ ছাড়বে সেদিন আওয়ামীলীগে একটি বিশাল দনধ হবে,0,politics
কিসের সাথে কি পান্তাপাতে ঘি,0,politics
স্যালুট ভাই ❤️,0,politics
আল্লা নূর ভাইকে হেফাজতে রাইখ আমিন বলেন সবাই,0,politics
শেখ হাসিনা খুনি হাসিনা,0,politics
তাই নাকি,0,politics
অনেকদিন ধরেই আপনার কথা আমি শুনতাম কিন্তু আলেমদের ব্যাপারে আপনি যখন কথা বললেন আপনার প্রতি তখনই আমার ঘৃনা জন্ম হয়েছে,0,politics
তুলনা হচ্ছে খালাদা জিয়া একজন সাবেক প্রধানমন্ত্রী ও অবাইদুল কাদের একজন নোয়াখাইল্লা।,0,politics
ত কি বুঝানো হল? এ ভিডিওর মাধ্যমে মূল কথা টা কি আপনার সেটা ত বললেন না,0,politics
রাইট বলেছেন আমি এক মত,0,politics
সাবেক প্রধান মন্ত্রীর সাথে খাওয়্যা কে তুলনা করা হাস্যকর,0,politics
এরাই নাকি জাতির ভবিষ্যৎ 😥😥😥😥 এর চেয়ে আমার মূর্খ অশিক্ষিত ভাইয়েরাও ভাল। আর যাই হোক তাদের মধ্যে মনুষ্যত্ব আছে,0,politics
ভালো ছিল,0,politics
গরিব,0,politics
স্যার তো টাকার কাছে বিকরি হইছে,0,politics
যতই পাম্প দাও কাজ হবেনা গেট আওয়ুট,0,politics
ছাত্রলীগ বেয়াদবদের বিচার চাই,0,politics
মরে নাই এখনো,0,politics
এই শিক্ষক গুলো হল ছাত্রলীগের গোলাম তাদের গালে গালে জুতা মারো তালে,0,politics
নীচের ঘটনা গুলুর সম্পের্ক লিখুন শান্তি বাহিনি র শাথে সরকারি বাহিনি আর্মি নেভি এয়ার পুলিশ লরাই এ নিহত আহতঃ শংখ্যা শান্তি মিশন এ আফ্রিকা –তে নিহত নিহত আহতঃ শংখ্যা জিয়াউর রাহমান এর ক্যু – এর সময় এ নিহত আহতঃ শংখ্যা ক্যু – এর পর কোর্ট মারশাল এ নিহত শংখ্যা ঢাকা বিশ্ববিদ্যালয় এ এর পর বিভিন্ন সময় নিহত আহতঃ শংখ্যা অন্যান্য শিখ্যা প্রতিস্থানে নিহত আহতঃ শংখ্যা নোয়াখালীর লোক নোয়াখালীতে নয় দূরবর্তী ন্থানে হরতাল অবরধ এ নিহত আহতঃ শংখ্যা এ শকল ক্ষেত্রে নোয়াখালীর নিহত আহতঃ শংখ্যা কত? শতকরা হার কত? দয়া করে জানাবেন কি? পিএ র কাছে লক্ষ টাকা পাওয়া গেছে সুরঞ্জিন সেন গুপ্ত অনেক দূরে তার মন্ত্রিত্ব যায় তো ্‌্‌ ্‌ ।,0,politics
নিজে নিজে সব বানিয়ে বলেন এটা বাংলাদেশের মানুষ জানে আয়ামিলিক কের চাকর রা 😂,0,politics
কিছু মনে করবেন না । আমার মনে হচ্ছে আওয়মীলীগ কিছু একটা ধামাচাড়া দেওয়ার জন্য সড়কের প্রতি বেশী নজর দিচ্ছে। এই সড়ক নিয়ে উত্তেজনা নিজেরাই করছে । এটাকে স্বভাবিক প্রক্রিয়ায় চলতে দেয়া উচিত। সড়ক নিয়ে এখন এত মাথা ব্যাথা কেন ? আগে কোথায় ছিল।,0,politics
কাউয়া মরল না কে,0,politics
ভাই তুই একটা জিনিস,0,politics
এভাবে মাইর খেয়েই যাবে যদি উল্টো মার না দিতে পার। যখনি হামলা শুরু করে তোমারও উল্টো হামলা করে তাহলেই সব সমাধান হবে এর আগেই নয়,0,politics
ভি পির উপর খামলা কেন। কি করে সরকার,0,politics
কাদের সাহেব বলবেন এইসব এডিট করা যাই ভাই,0,politics
শুধু ঘরিই?,0,politics
অপুর কথা শুনে কুত্তা ও তাঁর মুখে পেশাপ করবে না বিনএনপি পন্থী মহিলাটি কতো সুন্ধর বাসায় কতো বলছিলো ।,0,politics
যদিও কোন সম্পুর্ন কোন আইন নেই তবুও মানব জাতী হিসাবে হিন্দুদের নেএিত্ত  দেওয়ার উপযুক্ত কাউকে ভাবা  হয় । আন্না হাজারে সফল এ যুগে অন্য কেহ নয় । যেহেতু এখন গান্ধি খুদিরাম নেতাজী নেই মোদী রাহুল রা অহিংসের মর্ম বোঝে না । ওরা অহিংসের অমর্যদা কারী তাছারা কিছু নয় ।  যদি সে ভারত বর্ষ বিভক্তের কথা ভাবা হয় তার জন্য কায়দে আজম জেন্নাই দায়ী  অন্য  কেহ নয় । কু কৌশল করে অপশক্তিরা  ভারত বর্ষ নিসপেষন করছিল  সে কারনে নজরুল রক্ত ঝরালো জুলুমের স্বীকার হলো বার বার ঐকের ডাক দিল না খেয়ে জীবন উৎসর্গ  করল মুক্তির প্রেরনা জুযিয়ে  তবুও কেউ না বুঝুক জেন্না কেন বুঝলো না । ধরে নেওয়া যায় সেও মায়ার সাগরে হাবু ডুবু খাচ্ছিল কোরানের আইন বুঝত না কোরানের আইন বুঝলে এ পৃথীবিই হাতে থাকার কথা  শুধু ভারত বর্ষ  নাা । মমতাজ কে ভাল বেসেছিল সাজাহান কিন্তু কি শুনি আমরা নিজ হাতেই করেছিল খুন গরেছিল তাজমহল  এটা আবার কোন আইন কোন ধর্মে রোল । কেন বুঝিল না কোন খান্নাসে পাকরালো আমাদের এখনো নেই কারো হুস । কবে বুঝিব কবে হবে আমাদের জ্ঞান নাকি এমনি ভাবেই আসিব যাইবো কেউ বুঝিব না । না এটা তো কোরানের বানী নয় বুঝিলে তার বিজয় হবেই তাই কোরানে কয় । তাহাতে যে শুধু  শান্তির বানী হিংসা বিদ্বেস নাই । খ্রিসটান  আর বৌদ্ধ দের জ্ঞানের বহর হয়েছে ভারী তাই তারা শুরু করেছে শুধু ধ্বংশ বল প্রয়গ  কু কৌশল আর আরী ।  অর্থ সম্পদ যতক্ষন আছে ওদের বুঝালেও বুঝবে না । এটা ওদের নয় শয়তানের প্রবঞ্চনা । প্রত্যকের সঙ্গে রয়েছে শয়তান এ যে ছহী হাদীসের বানী । না করিতে পারিলে মুসলমান মানব জাতীর রাখিবেনা মান এটা  যে আমার নয় রাসুলের  ফরমান । ছারিবো না আমিও এ লেখা লিখিতে যতক্ষন আছে প্রান । যদি হক বলে কিছু থাকে তাহাকে ছারা কাউরে করিব  না পরোয়া সেই আমার  শক্তি  সেই আমার  শেষ ভরসা ।।।।।।।।।।।,0,politics
বাবতে লজ্জা লাগে এটা নাকি দেশের শিক্ষা প্রতিষ্ঠান,0,politics
ভাই রমিও গানের লিংক টা হবে??,0,politics
যারা অন্যায় করে তাদের আল্লাহ তাযালা ঘৃনা করে এবং তাদের আল্লাহ পছন্দ করে না।,0,politics
সেলুট ভাই,0,politics
ভাই তোমার চ্যানেল ব্যান্ড করে দিবে,0,politics
অপু পাগলি উল্টা পাল্টা বকে,0,politics
এরা কি পড়াশোনার জন্য ঢাকা বিশ্ববিদ্যালয়ে গেছে। ছিহ! ধিক্কার জানাই।,0,politics
বঙ্গবন্ধু কে হত্যার সময় আওয়ামীলীগ কোথায় ছিল এখন গলির কুত্তাটাও আওয়ামীলীগ করে।,0,politics
দেখ ইনু আওয়ামীলীগ যদি তর কাছে না থাকে তাহলে তুকে কুত্তার মত সবাই লাথি দিবে।ওবায়দুল কাদের সাহেব যা বলেছেন তা সঠিক। তুই আর কত চাটুকারিতা করবে।,0,politics
মাগনা পেলে আলকাতরা মাখাই যায়।এদের যেদিন ধরা হবে সেদিন কোনো বাপেই ছারতে পারবেনা,0,politics
মাননীয় প্রধানমন্ত্রী শেখ হাসিনা বলতে কষ্ট হয় বার বার শেখ হাসিনা বলা কি ঠিক হচ্ছে?,0,politics
কাওয়া কা কা কা,0,politics
এরা মনে হয় শুধু রাজনীতিই করে পড়া লেখা নাই। এর নাম আওয়ামীলীগ ।,0,politics
জয় বাংলার আগাছা কাটো,0,politics
পরীক্ষার আগের দিন রাতে টাকা দিয়ে ঘড়ি কিনেছিলাম! আরো কম দামি কিনতে চাইছিলাম কিন্তু পাই নি আমাকে কি জাতি মেনে নিবে না?,0,politics
দেশে উন্নয়ন না করে দেশের টাকা বিদেশে নিয়ে নিছে দেশ শাসন করার মতো খালেদার যোগ্য নাই তারেক জিয়ার যোগ্য নাই এখন দেশে শত করা জন মানুষ শিক্ষিত সাধারণ মানুষ সব কিছু বুঝ এখন,0,politics
অপু উকিল পুরাই অসুস্থ নাহলে সালে তারেক জিয়ার ক্ষমতা দখল ও মৃত ব্যক্তি কোকো নিয়ে এভাবে বলতে পারত না। এ তারেকের বয়স কত হয়েছিল মহিলাটার ভালো করে জানা দরকার ছিল।,0,politics
যারা এগুলো করে তারা ছাত্র না আসলে সন্ত্রাসী জাতির বিবেকের কাছে প্রশ্ন,0,politics
খালেদা জিয়া গনতন্ত্রের মা বিশ্ব চেনেন বাংলাদেশ প্রধানমন্ত্রী । আর ওবায়দুল কাদের সাধারণ সম্পাদক। কার সাথে কি পান্তা ভাতে ঘী। আওয়ামীলীগ শুধু পুলিশের দাপটে টিকে আছে। সাধারণ জনগণ ঘৃনা করে একরোখা সরকার কে। বছর বয়সী ছেলে মেয়ে বুঝতে পারে কি ভালো কি মন্দ।,0,politics
এক কাফের বলে না মুসলিম না হিন্দু এখন আর একটা পতন হবে,0,politics
আওয়ামী লীগের নেতা সকলটি চুর,0,politics
মহিলা উবায়দুকাদর ইস্তিরি কাফের কাদের ছাড়া কিছু বুঝেনা,0,politics
হাচা কথাই কইচে হেতে এই রকম নেতারি দরকার,0,politics
হাসিনা কি আবারও আগামিতে ভোট চুরি করে খমতা আসবে।,0,politics
আ ও য়াম লেগে কি কোন রাজাকার নেই,0,politics
স্যার নয় ওটা শয়তান,0,politics
ডাকাতি করে বড় দল করেছ?তোমাদের এই ডাকাতি একদিন না একদিন বন্ধ হবে ইনশাআল্লাহ,0,politics
বুলু বিনোদন ছাড়া আর কিছুই না,0,politics
আসলে কি বাঙালির সুখে থাকতে ভূতে কিলায়।আসুক আবার ক্ষমতায় আসুক জামায়াত বি এন পি। জেলায় সিরিজ হামলা যখন জামায়াত বি এন পি করেছিল ওইটাই আমাদের ভাল ছিল।আবারো আমাদের এইগুলাই দরকার।,0,politics
কিছুদিন আগে প্রধানমন্ত্রী শেখ হাসিনা ভারত সফর করে এসেছেন। ঐ সময়টায় যখন ভারতের অর্থনীতির মন্দা কে কেন্দ্র করে প্রতিটি ভারতীয় গণমাধ্যমে তোলপাড় চলছিলো।তখন বিবিসি হিন্দির ইউটিউব চ্যানেলে ভারত ও বাংলাদেশের অর্থনৈতিক অবস্থাকে তুলনা করে একাধিক ভিডিও প্রকাশ করেন।আর এ বছর নির্বাচনে আওয়ামিলীগের তথাকথিত বিজয়ের পর ও তারা একটি ভিডিও প্রকাশ করে যেটাতে উল্ল্যেখ করেন যে আওয়ামী সরকার ক্ষমতায় থাকলে ভারতের কি কি উপকার সহ ইত্যাদি বিষয় নিয়ে।বিবিসি হিন্দি কেন ভারতের পররাষ্ট্র নীতিকে মাথায় রেখে সব সময় তাদের বাংলাদেশ কেন্দ্রিক কন্টেন্ট গুলো বানিয়ে থাকে? বর্তমান ভারতের টিভি চ্যানেল গুলো প্রায় ই সরকারের হয়ে কথা বলে এবং হিন্দু মুসলিমের মাঝে বিবাদ সৃষ্টি হবে এমন কন্টেন্ট তৈরি করে।যারা প্রোগ্রেসিভ আর সৎ ব্যক্তি বর্গ যারা সেকুলার সুশিল সমাজের ব্যক্তিবর্গ আর সাংবাদিক তারা ইউটিউব এবং বিভিন্ন মোবাইল এপ কে মুক্ত গণমাধ্যম হিসেবে বেছে নিয়েছেন।নিজের দেশ সম্পর্কে তারা সঠিক তথ্য দিয়ে জনগণের প্রতি সুবিচার করেন।কিন্তু আমাদের দেশ সম্পর্কে কোন ভিডিওতে কোন মন্তব্য করলে দক্ষিণ এশিয়ার একমাত্র বন্ধু রাষ্ট্র বলে আখ্যায়িত করনে অথবা শেখা হাসিনা র মতো লিডার এমনটা বলে থাকেন। ওদের সিভিল সার্ভিস পরীক্ষা কে কেন্দ্র করে বিভিন্ন নামী দামী ইউটিউব চ্যানেলে অনেক ভালো ভালো গুণগত সম্পন্ন ভিডিও বানায়। আর যেকোন দেশ সম্পর্কে বলতে গেলে ওরা খুটি নাটি পক্ষ বিপক্ষ আল্লাহর নামে সবটা দেখায়।এমনকি আমাদের বাকশাল নিয়ে বলতে গিয়ে তারা বঙ্গবন্ধু কে ডিকটেটর রুপে দেখেছেন।কিন্তু বর্তমান অবস্থা নিয়ে বলতে গেলে এক চেটিয়া উন্নয়ন আর ভালো লিডারশীপ দেখান।এরপর রিএকশন চ্যানেল আলারা তো উন্নয়নের ভিডিও দেখে আহ্লাদের চোটে বাচে না।স্যার কেমন যে লাগে ঐগুলা দেইখে।মিথ্যা চাটুকারিতা শুনার চেয়ে বদনাম শোনা অনেক ভালো।,0,politics
বাংলাদেশের আওয়ামী লীগ নোংরা রাজনীতি করতে করতে এতটাই মেন্টাল হয়ে গেছে যে ওরা রাতকে দিন বানিয়ে দিচ্ছে দিনকে রাত বানিয়ে দিচ্ছে কোথায় বেগম খালেদা জিয়া আর কোথায় কাউয়া কাদের বলার কিছু ভাষা আর নাই আমাদের,0,politics
ইস,0,politics
ভাই এখন ভাল লাগল কারণ আপনি সতত বলেছেন ।,0,politics
ওবাইদুল কাদের স্যারকে সুস্থ করার সহজ উপায় হলো উনার কানের কাছে গিয়ে বলেন তারেক জিয়া দেশে আসছে বিএনপির হাতে ক্ষমতা চলে যেতে পারে! দেখবেন এক লাফে উঠে যাবে,0,politics
ওবাইদুল কাদেরের স্ত্রী মনে হয় নাকি সতিন?,0,politics
নাইচ,0,politics
ডিক,0,politics
খালেদার সাথে তো হাসিনারই তুলনা করা যায় না কিসের কাদের হিরার সাথে প্লাস্টিকের তুলনা,0,politics
খারে ভাই খা।,0,politics
বঙ্গবন্ধু চোর খুজেছিলো আপনি সেই চোর বের করে দিলেন। মন থেকে স্যালুট ভাই।,0,politics
ভাই রাগ করেন কে? আপনিও ষ্টুডেন্ট সেও স্টুডপন্ট।,0,politics
তুমি জিনিস,0,politics
সবাই মিলে স্বাগতম জানাই নতুন দল ডিম লিগ এর জন্য 😄😄😄,0,politics
বাংলাদেশের গণমাধ্যম সরকারের পা চাঁটার দল। তাই কাদিরার ঘড়িদুর্নীতির খবর প্রকাশের মুরোদ নেই,0,politics
প্লিজ এমন করবেন না। ছবি তুলেই চলো যাবো।,0,politics
নুরু ভাই আমি আপনার ওপরে আছি🙈,0,politics
নূর ভাইের কথাই ঠিক,0,politics
সাহেদ আলম ভাই আপনি ইলিয়াছ ভাই কে নিয়ে অনেক বাজে কমেন্ট করছেন তাই আপনার চ্যানেল থেকে বিদায় নিলাম ভালো থাকেন।,0,politics
আপনি চেক করতেসেন ভালো কিন্তু সামনে এবং পিছনে যে যেম লাগসে সেটা কি কাঙ্খিত?? আপনার উচিৎ সব ঘুষখোর পুলিশ অফিসাকে খুজে বেরকরে তাদের সাজার ব্যবস্তা নেয়া তাহলে দেখবেন গাড়ীর লাইসেন্স কাগজ ছাড়া কেউ গাড়ী বের করবেনা পুলিশ কে করাপ্টেড মুক্ত করলে দেখবেন দেশ ও জাতির মঙ্গল হবে সব পুলিশ খারাপ না কিছু ভালো পুলিশ ও আছে বাট তাদের দেখা ভাগ্যের ব্যপার,0,politics
ভাই আমার দোকানের একটি এড করবেন? যদি এডটি করেন আমার অনেক উপকার হবে আমার দোকানের নাম নিউ খান এম্পোরিয়াম কর্ণফুলী গার্ডেন সিটি শপিং কমপ্লেক্স কাকরাইল ঢাকা মোবাইল নং,0,politics
আমার কোন হাত ঘড়ি নেই। মোবাইলে অথবা দেয়াল ঘড়ি দেখে সময় জেনে নেই।,0,politics
এই গণতন্ত্র মিছে মোহ মন্ত্র শোষণের যন্ত্র পশ্চিমাদের। এই গণতন্ত্রে সৎ কি বা অপরাধী মূর্খ বা শিক্ষিত সবাই ভোটার সবার ভোটের মান অংকে সমান তাই দুষ্টুরা পথ খুঁজে পায়দা লুটার এই গণতন্ত্র মিছে মোহ মন্ত্র শোষণের যন্ত্র পশ্চিমাদের। এই গণতন্ত্রে ব্যক্তি গণনা হয় ব্যক্তির কবু হয়না ওজন প্রার্থীর তালিকায় সকলেই ঠাঁই পায় মন্দ অমন্দ নেই বিভাজন এই গণতন্ত্র মিছে মোহ মন্ত্র শোষণের যন্ত্র পশ্চিমাদের,0,politics
তাদের এত কোটি কোটি টাকা আছে সেখানে কোটি টাকার ঘড়ি পড়তেই পারে এটাই তাদের জন্য স্বাভাবিক।,0,politics
খালেদার সাথে কাওকে তুলনা করা জাবে না কারন খালেদা ইতিমের টাকা চুরি করে জেলে,0,politics
দুদ গুল দাএ কেতে,0,politics
দুর মিয়া ঘড়ি বুঝি এত দাম পাগলের প্রলাপ,0,politics
টিক আছে আপা,0,politics
এরকম সাহসি ইউটুবার কোনো দিন দেখিনি,0,politics
ব্রো আমি তোমার গানগুলো বেশী ইনজয় করেছি😁🤣 সত্যিই আমি শিহরিত🤓,0,politics
ওবায়দুল কাদের ভালো করে কথা বলতে জানেনা,0,politics
বেগম খালেদাজিয়া বাংলাদেশের কোটি মানুষের হৃদয়ের স্পন্দন তার সাথে কাদেরের তুলনা চলেনা।,0,politics
নঅ,0,politics
নুরবাই এগিয়েছলু আমরাআছি তুমারসাতে কোনুদলবুজিনা দেশবাচাতেহবে ইসআলল্লা,0,politics
এর লিং কাজ করছে না ভাই,0,politics
সাবাস ব্রো,0,politics
ওবায়দুল কাদেরের পায়ের সামনেও যেতে পারবে না খালেদা জিয়া।,0,politics
আম গাছে আম ধরে চুতরা গাছে চুতর বাঘের ঘরে বাঘ হয় কুত্তার পেটে কুত্তা! যার নেত্রি যেমন তার কড়ী ও তেমন।,0,politics
ঐদিন এত সাংগাতিক রা কোতায় চিল যে কোমলমতি চাত্র দের ওপর হামলা করো হেলমেট বাহিনি,0,politics
ডিমের দাম তো বেশী হয়ে যাবে।।,0,politics
এগুলো সব দেশের টাকা সালা চোর,0,politics
এখানে বিএনপি বা জামায়েত এর হাত আছে হাহহায়া,0,politics
ভাই মজনু কে নিয়ে একটা ভিডিও বানান,0,politics
রা এপ্রিল । বাংলাদেশ ডিম লীগের প্রতিষ্ঠাবার্ষিকী স্বমহিমায় পালিতে হবে।,0,politics
আর কি দেকবো ভাই,0,politics
ফিটনেস বাড়ীতে আছে সার,0,politics
বিএনপি সরকার তারা শুধু মুখে বক বক করে কাজে বেলাতে,0,politics
পদ্মা সেতুর টাকা 😂😂😂😂,0,politics
খালি একটা কথা বলি পাপ বাপ কেউ ছাড়ে না।,0,politics
কোটি টাকার ঘোরি পরে এই টাকা ও পাইলো কোই জনোগনের কাছে জবাব দেয়াহোক,0,politics
ধন্যবাদ স্যার সাহেদ আলম।,0,politics
ভাইয়া আগিয়ে যা ও ❤ কিন্তু ভয় হয় সত্যি কথা বলতে গিয়ে তোমার না কিছু হয়ে বসে😞 আর তোমার জন্য ভালোবাসা অবিরাম ❤❤,0,politics
ভাইয়া তুমি একটা জিনিস,0,politics
দেশে অাবার যুদ্ধ হবে সেটা কুত্তা লিগের সাথে,0,politics
আপনার কথাগুলো শুনি এত এত ভালো লাগলো কি দিয়ে আপনাকে ধন্যবাদ জানাবো আপনার মত নেতা প্রত্যেক ঘরে ঘরে জন্ম নেওয়া উচিত।,0,politics
রাজাকার দের কোনো জায়গা নাই,0,politics
স্যার আপনি কি কনো দিন মরবেন না,0,politics
কাদেরকে বাদ দিলে ভাল হবে,0,politics
বি এন পির নষ্ট দল হওয়ার কারন হলো মউদূদীর উম্মত জামাতি শয়তানের দলের কারনে,0,politics
এদের কে ধরে ফাঁসি দেওয়া উচিৎ। যারা নুরের উপর হামলা চালিয়েছে । স্বাধীন বাংলাদেশের মানুষ আজও স্বাধীন হয় নাই । এদের কে পায়ের তলায় পিশে মারা উচিৎ।।,0,politics
হা হা হা হাসব না কানব যেই সরকার এর মন্ত্রী বলে পাচ কোটি টাকা কোন টাকা নই।সেই সরকার তেকে আবার জন গন কি আশাকরে।,0,politics
কাদেইররা আল্লাহকে ভয় কর হারামজাদা। মরতে মরতে ফিইরা আইছোস। আল্লাহকে ভয় কর।,0,politics
ওবায়দুল কাদের হলেন বাংলাদেশের সব চেয়ে দুর্নীতিবাজ।ওবায়দুল কাদের এর মত লোক যে রাজনৈতিক দলে থাকে সে দলটা অচিরেই ধবংস হয়ে যাবে।,0,politics
আগুন নিবার এক মাত্র অসুদ পানি তাই দিয়েছে,0,politics
পাগলিটা মা হয়েছে বাবা হয়নি কেউ দেশটা অনেক আগে স্বাধীন হলো মানুষ হয়নি কেউ,0,politics
শুদু কাদের না হাসিনা ও খালেদার সমান হবেনা,0,politics
রাস্তায় জ্যাম লাগানোর কৌশল,0,politics
চলিতাছে সার্কেস,0,politics
ভাই ডক্টর এর কাছে যাচ্ছি ভাই আমার হাসী থামেনা ভাই??,0,politics
আমার রোলেক্স ঘড়ির অনেক সখ কিন্তু রেপ্লিকা কিনার টাকাই নাই কাদের ভাই যদি দিত তার পক্ষে স্লোগান দিতাম আর সারা জীবন তারে ভোট দিতাম 🤣,0,politics
পকেটে খরচ করার মতো টাকা নাই তাই রাস্তায় বের হয়ছে,0,politics
কয়েক বছর আগে কাদেরের নাম কোথাও আমি শুনিনি,0,politics
সততাই মূলধন সততা ও নিষ্ঠার সাথে কাজ করলে দেশ ও জাতি সকলেরই ভালো হবে।,0,politics
অসাধারণ! শাহেদ ভাই আমি আপনার ট্রেস পাচ্ছিলাম না আর সেই আজকে যখন আপনার ইউটিউবে সাবস্ক্রাইব করেছি। আর আপনার সাথে আমার কিছু কথা তাহা আমি কোথায় কখন পাবো সেটার প্রচেষ্টায় আমি অবিরত থাকবে!,0,politics
এখন কাদের সাহেব বলবেন এইগুলো আসল না পাটুয়াটুলির কপি মাল 😂😂😂।,0,politics
বাংলার মানুষ গরিব তাই তারা গরিব মানুষকেই তাদের দেশের সরকার হিসাবে চায়।কারন গরিবই গরিবের দুঃখ বুজে। ভোট চোর সরকার বাংলাতে একজনই সে হলো হাসিনা,0,politics
নুরু তুই এবার অফ যা,0,politics
কি অবস্থা,0,politics
বঙ্গবন্ধুর খুনি ইনু ইনুর দিন শেষ। জামাতের দিন শেষ জামাতের শরিক দল শেষ সার্কাস পার্টি দিয়ে আর কি হবে।। ইয়ানফসি কর বাসায় বইসা দিন গুনতে থাক বিচার সামনে রেডি তুমার জন্য। জাসত বাসত দিয়ে আর কাজ হবেনা।।,0,politics
সেরা অভিনেতা,0,politics
পরীবতন করে ইনকাম করার জাইগা করে দেওয়া আর কিছু না,0,politics
রুমিন ফারহান,0,politics
আপনি ভাই একদম হিরো ভাই। ভালোবাসা অবিরাম ভাই💗,0,politics
ছি ছি ছি ওবায়দুল কাদেরের এই অবস্থা!!! যে দেশের মানুষ খেতে পায় না যে দেশের মানুষের কর্ম নাই যে দেশের মানুষ দুর্নীতির মধ্যে পড়ে থাকে সেই দেশের এই ভাবে বড়লোকি পানা!!! ছি ছি ছি!!!,0,politics
এইলোকটা পাগল ছাড়া আর কিছুই নয়।উনি রাস্তায় নামছেন।কেন?দেখাইবার লাগছে।,0,politics
কার সাথে কার তুলনা,0,politics
এগিয়ে যান নুরুল হক ভাই,0,politics
বাটপার লীগ,0,politics
অপু ওকিল জুতা পেটা করা দরকার,0,politics
আওয়ামী লীগ ভোট চোর,0,politics
নুরু ভাই সত্যি সাহসী!,0,politics
এই দেশের সব মূর্খ মানুষগুলো রাজনীতি নিয়ে পড়ে থাকে।বিজ্ঞানের চিন্তায় নেই নেই ইসলামের চিন্তায়ও।,0,politics
ভাই আপনার নতুন ভিডিওর অপেক্ষায় ছিলাম দোয়া ও শুভ কামনা রইল,0,politics
ভাই মোস্তাফিজ আমাদের জেলাঃ চট্টগ্রাম থানা বাঁশখালীতে অনেক খারাপ লোক,0,politics
বাংলাদেশের প্রথম প্রধানমনএি তাজ উদদীন আহমেদ তাই ওনার ছেলে সাধারণ সম্পাদক পদ পাওয়ার জন্য মাননীয় প্রধানমন্ত্রী কে বিনিত ভাবে অনুরোধ জানাচ্ছি।,0,politics
নিজেকে নিয়ন্ত্রণ কর। তারপর অন্যকে অনুশাসন কর। নিজে নিয়ন্ত্রিত হলে অন্যকেও নিয়ন্ত্রণ করতে পারবে। নিজেকে নিয়ন্ত্রণ করাই কঠিন।,0,politics
আমি শুনেছি ওবায়দুল কাদরের আান্ডাওয়্যার ও বেশ দামী এটার উপর একটা ভিডিও বানানো যায় কি না দেখেন। জাতি উপকৃত হবে।,0,politics
ভাই তার আছে সে পড়ে আমাদের নাই আমরা পড়তে পারিনা।,0,politics
ভারতীয় রাজাকার মুক্তো বাংলাদেশ চাই,0,politics
বাঘের বাচ্চা,0,politics
বিজনেস আছে তো! সেতুর বিজনেস,0,politics
সাতটি ঘড়ির দাম এত কম,0,politics
লাইভ এ এসে বিড়ি খেলেন এমপি জাহাঙ্গীর কবীর নানাক এমপি যুগ্ন সাধারণ সম্পাদক বাংলাদেশ আওয়ামীলীগ,0,politics
ওটা কি নোমো,0,politics
খালেদা আর হিরো আলম সমান,0,politics
তোমার মত কুলাংগারকে দেশের মানুষ কেমন ঘৃনা করে নিরপেক্ষ নির্বাচন হলে বুঝতে পারবে।জনগনের অধিকার হরন করে শোষক হওয়া যায় কিন্তু নেতা হওয়া যায় না,0,politics
আর হাছিনায় দুই বার ভোট ডাকাতি করে খমতায় আছে এই মহিলা ত নিজেও জানে,0,politics
এগুলা তো একটা যোকতির কথা,0,politics
ওবায়দুল কাদের এর পায়ের যোগ্যতা তো হবে না খালেদা জিয়ার। মানুষ একজন শিক্ষিত ছেলের সাথে অশিক্ষিত মূর্খ মহিলার তুলনা কেমন করে।,0,politics
এতো চামচা সাথে চমক,0,politics
খালি পেটে বাকিরা আর কতদিন থাকবে তাদেরকে পেটভরার সুযোগ না দিলে হয়তো তারা দলে থাকবে না দল থেকে বের হয়ে যাবে তাই দলের স্বার্থে তাদেরক পেট ভরার সুযোগ করে দেওয়া হবে,0,politics
বিএনপি অকারণে এই শিক্ষাদীক্ষাহীন মহিলাকে পার্টি প্রধান হিসেবে ধরে রেখেছে বিএনপি র সিনিয়র নেতারা এ ধরণের ভুলের মাঝে আর থাকা উচিত হবে না। তাদের উচিত হবে এই মহিলাকে অবসরে পাঠিয়ে দিয়ে বিএনপি কে পুনর্গঠিত করে সুস্হ রাজনীতিতে ফিরে আসা এতে বিএনপি ও জাতি উপকৃত হবে বিএনপি মৌলবাদ মুক্ত হয়ে আধুনিক রাজনৈতিক দল হিসেবে ভুমিকা রাখতে পারবে।,0,politics
কৈ আব্দুল কৈ খালকুল।,0,politics
রাইট জানতে পারলাম জানতে পারলাম জানতে পারলাম💯💯💯,0,politics
ওই ছাড় ওদের সাথে জড়িত আছে,0,politics
ওবাইদুল কাদের বর খালেদা জিয়া একজন বদরাগি মহিলা কাদের সরক মন্ত্রী হলেও যে উন্নয়ন করেছে তা খালেদা জীবনেও করতে পারবেনা,0,politics
ফালতু খবর।মেঘনা গ্রুপ এর শেয়ার এর কথা কে বলবে।,0,politics
কে কে আমার মত কাদের ঘড়ি দেখতে তার ফেসবুক পেজে টু মারছেন?,0,politics
হাঠার মামু আচে নাকি কাদের হাঠা,0,politics
!! মন্ত্রী বানাবো আমি মন্ত্রী বানাবো আমার ছেলেকে আমি মন্ত্রী বানাবো !!!,0,politics
সব থার্ড ক্লাসের ছাত্র ছাত্রী এন্ড স্যার গুলোও তেমনি দেখলাম পয়দা হয় এখানে এর চেয়ে প্রাইমারী পাশ করে চলাটাই অনেক ভাল ভদ্রের আওতায় থাকতে পারবে সমাজ,0,politics
বাহ উনাকে সুন্দরীদের চারপাশে থাকতে হয়না? তাছাড়া এবার মালাকুল মউত এর হাত ফসকে বেরিয়ে আসতে পারলেও জাক্কুম বৃক্ষ যে ছাড়বে না শেষমেশ তা তিনিও জানেন।তাই জোর করেই জনগণের টাকায় ফুটানি চালিয়ে যেতে চান !!😂😂,0,politics
কেন জানি ভাই আপনাকে ভালো লাগে না আপনাকে দুই মুখো সাপ মনে হয়,0,politics
উনার বিষয়ে সুষ্ঠু ভাবে তদন্ত করলে আগে যা কিছু হইছে সকল কিছুর রেকর্ড ভাঙবে !!,0,politics
এখানে পড়া লেখা হয়। নাকি শুধু রাজনীতি হয়। থুথু মারি এমন ছাএ ছাএির।,0,politics
হায়রে নুরু এতো নাটক। শিক্ষা প্রতিষ্ঠান টাকে ধঙশ এবং শিক্ষা পরিবেশ টাকে খাইলা। কুকুর আসিয়া কামর দিল পথিকের পায়।পথিক কি কামর দিতে পারে কুকুরের গায় । সারাক্ষণ ছাত্রলীগ কে দোষাচছ কিন্তু তোমাদের মধ্যে নূন্যতম ভদ্র তা ও নাই। ছাত্রলীগ খারাপ তোমরা তো তার চেয়েও জঘন্য।লেখা পড়া করতে আসনি এসেছ রাজনীতি করতে । রাজনীতি করতে আসলে প্রতি পখ তোমাকে রাজনীতিক ভাবে মোকাবেলা করবে এটাই তো নিয়ম। তুমি সালা নোংরা পরিবারের নোংরা সন্তান। শিক্ষার পরিবেশ টা অনেক ভালো ছিল তুই গরু শিক্ষার পরিবেশ টা খাইলি।এক পক্ষকে দোষ দিলে চলবে না তুমি সালা ছাত্রলীগ এর চেয়েও খারাপ তোমার জন্মর দোষ আছে। প্রতিটা পরিবারের ছেলে মেয়েদের শিক্ষার জীবনটা ঝুঁকি পুর্ন করতেছ। একদিকে ছাএদের নিয়ে রাজনীতি করতেছ আরেক দিকে বর্তমান সরকার কে ভোট চোর আখ্যায়িত করতেছ ফের মা ডেকে ছালাম করছ । তোমার আসল রূপ তো চেনা বড়ো মুস্কিল। তুমি সালা বিঙস সতাবধিতে এসে হিটলার কেও হার মানিয়েছ। তোমার ভবিষ্যৎ অনিশ্চিত ও অন্ধকার এটি বেশি দূরে নয় ।অতিব বড় হইওনা বাতাসের তোড়ে ভেসে যাবে টিকতে পারবে না বাস্তব বড় কঠিন। তুমি বঙ্গবন্ধুর মতো নেতা হতে চাও তাইনা আমরাও আসাইরহিলাম।,0,politics
কার সাথে কার মিল খোঁজো অপু মিথ্যুক চাপাবাজ খালেদা জিয়া গণতন্ত্র ও মানুষের বাক স্বাধীনতার আপোষহীন নেত্রী অপরদিকে গণতন্ত্রকে হত্যা ও মানুষের মৌলিক ভোটাধিকার খর্ব করার নেত্রী হাসিনার একজন সহকারি নোয়াখাইল্লা চিটার কাউয়া কাদের তদের তো লজ্জাই নাই লজ্জা কাকে বলে আগে শিখ জনগণের কাছে ক্ষমা চা,0,politics
আমার মনে হয় আওয়ামী লীগ সমর্থক রায় এবং আওয়ামী লীগ মন্ত্রীরা এবং আওয়ামী লীগের নেতৃত্বে যারা তাদের সবাইকে বলছি গণতন্ত্র কাকে বলে আপনার কিছুই জানেন না,0,politics
রাজাকার এর কথা যে বললেন আমাদের সরকার দলীয় আপা এখন যে অরিজিনাল রাজাকার এর লিস্ট কোথায় সাকা চৌধুরীর নাম কোথায় ইসলাম এর বাণী পেশ করার আলোড়ন সৃষ্টীকারি দেলোয়ার হোসেন সাইদির নাম কোথায় সেই বিএনপি সংসদ গঠিত করা সেই সব সদস্য দের নাম এখন তো আপনারা এই পাকিস্তান এর দেওয়া লিস্ট জনসম্মুখে আনছেন না এতো কিষের ভয় আপনাদের সালে সেই আগস্ট আমাদের দেশের একজন বড় নেতা কে যেই বাহিনির লোক নেতার সপরিবারের সবাই কে হত্যা করেছিলো সেই তো আজ আপনাদের সংসদ সদস্য প্লাস মন্ত্রী কি বুঝবে বাংলার জনগন বাটপারি কে করছেন,0,politics
অপনাদের থেকেই শুরু হবে ঘরোয়া যুদ্ধ যায়গাতেই পালটা জবাব 🤝,0,politics
সব কিছুর মধ্যে ও সকল কাজ কর্ম ঠিকই আছে টাকা মালেশিয়া পাচার হচ্ছে কিনা,0,politics
আজ য‌দি নুর ছাত্রলীগ করত হয়ত তার উপর হামলা করত না । নুর সম‌য়ের সাহসী নেতা । তোমার ম‌ধ্যে আগামীর ভ‌বিষ্যৎ দে‌খি ।,0,politics
কাউয়াকে দল থেকে বাদ দেওয়া ওচিত,0,politics
আমার দোয়া রইল এবং কি বিশ কোটি মানুষ আমাদের সাথে বি এন পি আসবে খমতা ইনশয়আল্লাহ,0,politics
এটা অসম্ভব আমাদের খালেদার জিয়ার সাথে ওয়াবাদুল কাদেরের তুলনা করা যাবে না,0,politics
ইতিহাসের সেরা বিদ্যাপিটে এমন সএাস,0,politics
আওয়ামিলিগের দালাল কে লাথি দিতে হয়,0,politics
ভালো জানতাম লোকটাকে তলে তলে এইকাম,0,politics
ঠিক ঠিক শতভাগ ঠিক,0,politics
সাহসী উপস্থাপনা। আল্লাহ ভাইদের সাহস আরো বাড়িয়ে দিন!,0,politics
মন্রী নিজের লাইন্স তো নাই বিনা ভোটে মন্তী,0,politics
কাদিরিয়া রাস্তার চেলে,0,politics
হিংসা হয়!!!,0,politics
ফকরুল বড় না হাছিনা বড় উওর ফকরুল,0,politics
ফেরাউন ও নমরুদের মতো এই ছাএলীগদের মৃত্যু হবে ইশাআল্লাহ্,0,politics
এমন একদিন আসবে ডিমলীগের অস্তিত্ত থাকবে না।,0,politics
এদের শাওয়ার চুল আগুন দিয়ে পুড়িয়ে দেওয়া ঠিক কার সাথে কার তুলনা,0,politics
ছোট ভাই তোমাকে অসংখ্য ধন্যবাদ । তোমার কৌতক ষ্টাইলে কথা গুলো খুব ভাল লাগে। সৌদি আরব হতে,0,politics
পাগলে কিনা কয় ছাগলে কিনা খায়,0,politics
ফাটা খেষ্ট নাকি??,0,politics
কোথায় বদহজম কোথায় কায়েদে আযম।,0,politics
ভাই রে ভাই তুই এই কালা বাদুরটারেও ছার দেছ নাই ?? তুই তো বেটা মরবি । আওয়ামীলীগ সরকারের আমলে আমরা সব রোবোট হইয়া বইয়া আছি আর তুই মানুষ হইলি ক্যামনে ??,0,politics
সব শয়তান এক সাথে,0,politics
সে যেহেতু ঘড়ি গুল বকশিস পায় সেহেতু হয়তো এগুলোর দাম ও তিনি জানেন্না।,0,politics
আওয়ামিলিক একটা পালতো দল,0,politics
বিশুদ্ধ করতে গেলেতো অাওয়ামিলীগ অার ক্ষমতায় থাকবে না।,0,politics
শাহেদ ভাই আপনি এভাবেই তদন্ত চালিয়ে যান। আমরা আছি আপনার সাথে। 👍 আপনার ভিডিও খুব ভালো লাগে আমাদের কাছে♥,0,politics
নিরলজ্জতা সীমা ছাড়িয়ে গেছে আমাদের।,0,politics
সবাই স্রোতে গা ভাসায় না।। যেমন আপনি।।।,0,politics
অপু উকিল কে চর মারতে ইচ্ছে করছে সামনে পাইলে আমি দিতাম,0,politics
বাংলা দেশের জন্য এটা ভয় কারন বাংলা দেশ আবার সাদিন করতে হবে,0,politics
বাংলাদেশের সন্ত্রাস বন্ধ করতে গেলে প্রথমে ছাত্ররাজনীতি বন্ধ করতে হবে ছাত্র রাজনীতি যতদিন করবে ততদিন বাংলাদেশের ভিতরে কোন খারাপই নারী দর্শন ইয়াবা চলবে যতদিন পর্যন্ত ছাত্র রাজনীতি বন্ধ না করবে বাংলাদেশ কখনো শান্তি পাবে না আমরা চাই বাংলাদেশের মানুষ বাংলাদেশে সুষ্ঠু ভাবে চলাফেরা করতে কিন্তু বর্তমানের ছাত্ররা যেভাবে অন্যায়-অপরাধ করে চলেছে বাংলাদেশ কখনো শান্তি ফিরে আসতে পারে না,0,politics
কাকে বর্জন করা উচিত ঢাকা বিশ্ববিদ্যালয়কে না ওখানকার শিক্ষকদের নাকি ছাত্রলীগকে নাকি নুরুলকে?,0,politics
বেআদব মহিলা তুমি কেন বাপের নিকট গেলে ।,0,politics
ধিক্কার জানাই এই রাষ্ট্র ব্যবস্থার যেই রাষ্ট্রে দুর্নীতি বাজ রা মন্ত্রী হয়।,0,politics
আরে আমাদের কাদের সাহেব যে!,0,politics
তোমার মতো ইনু ছারা আওয়ামীলীগ খুব ভালো চলবে প্রধান মন্তীকে ধন্য বাদ এই খারাপ লোক কে মন্তীত না দেওয়া,0,politics
সাহেদ ভাই এটা নিশ্চয়ই বিএনপি জামায়াতের চক্রান্ত 😅😅,0,politics
জনগণের টাকা লুট কোরে কিনেছে,0,politics
ওবায়দুল কাদের এর সাথে একটা লোক তুলনা করা যায়। সে হল হিরো আলম।,0,politics
এর শেষ কোথায় বাংলাদেশ আজ কোথায় যাচ্ছে,0,politics
কাউয়া কা কা কা,0,politics
দুঃখের বিষয় হল জানাচ্ছি যে রাজনীতি এমন একটা নোংরা বিষয়বস্তু যেখানে শিক্ষিত নামিদামি লোক কেউ সম্মান দিতে জানে না তাও আবার নিজ দলের ব্যক্তি কে,0,politics
ওবায়দুল কাদের একজন সাধারণ সম্পাদক তার সাথে চেয়ারপার্সন বেগম খালেদা জিয়ার কিসের তুলনা?,0,politics
শিক্ষক হয়ে দালালী করতে গেলে এভাবেই ঘৃণিত ও অপমানিত হতে হয়।,0,politics
নুর ভাইয়ের কিছু হলে,0,politics
ওবায়েদুল কাদেরের সাথে তুলনা করা হয় ভাদাইমার সাথে ভালো মিলবে। ওবায়েদুল কাদের তো আস্ত একটা চোর। সে মানুষের কাতারে পড়ে মনে হয়না। আমি আওমীলিগ করি আমি ন্যায়ের পথে কথা বলব। দূনিতীবাজদের কথা বলবনা। রুমিন আপু এগিয়ে যান।,0,politics
কি আর বলবো বাংলাদেশের যে অবস্থা দেশের টা বেজে গেছে,0,politics
এগুলো কি হচ্ছে দেশের,0,politics
নোয়াখালীর রত্ন,0,politics
সাি,0,politics
আমি কাইয়া কাদের বলছি গুজবে কান দিবেননা সায়েদ আলম গুজব ছরাচ্ছে,0,politics
ইনু সুযোগ পেলে হাসিনা কেও ফাটাবে,0,politics
কউয়া ওয়া ওয়া,0,politics
জিনজিরা!!!,0,politics
ভাই ভালো একটা ভিডিও আমাদেরকে অপু হার দিলেন দন্যবাদ আপনাকে,0,politics
মানবদেয়াল থেকে নিছে নাকি দামি পোষাক দামি ঘড়ি🤣🤣,0,politics
নুরাকে দেখা মাত্র পিডাইতে হবে,0,politics
শাহেদ আলম ভাই খুব ভাল লাগলো ভিড়িওটা দেখে ধন্যবাদ,0,politics
চুতিয়া থুড়ি মতিয়া চৌধুরী হাসিনার বাপের চামড়া দিয়ে ডুগডুগি বাজানোর আশা নিয়ে এসেছিলো তাতো পূর্ণ হয়েছে এখন কি হাসিনার চামড়া দিয়ে ডুগডুগি বাজানোর পরে মরবে?,0,politics
মেয়াদের মন্ত্রিত্ব ।আওয়ামী লীগের সভাপতি। ক্ষমতার সর্বোচ্চ চূড়ায়। কতটুকু কুটকৌশল তার আছে আমরা কতটুকুই বা জানি? এইসব দেখলে বিশ্বাস কি রাখা যায়? সাধারন জনগন হিসেবে?,0,politics
উনাকে প্রায় লাখ টাকা দিয়ে ঘড়ি দিয়েছি শুধু তিনবেলা তিন মুঠো খাওয়ার নিশ্চিয়তা দেয়ার জন্য।,0,politics
নাইস,0,politics
পুরনো আর ভাল লাগেনা।,0,politics
আমি চাই ভাইয়া কে কোন পদে রাকা হক আমি তেকে বলছি এবং করছি,0,politics
অপু উকিল তো মানুষের পর্যায়ে পড়েনা তারপরেও ভ্যা ভ্যা করে হারামজাদি কিভাবে মিথ্যাচার করে,0,politics
হাসিনা কেনো থাকবে। অকে পালটান,0,politics
হালার পো।।,0,politics
হীরে আলম বড় না কাদের বড়😄💖😄😄😄😄😄,0,politics
কাকের তুলোনা খালেদাজিয়ার তুলোনা হাহাহা,0,politics
এতো মানুষ নিয়ে লাইসেন্স চেক করলে পুরু রোড তো জ্যাম লাগবে এটা কি মন্ত্রি সাহেব বুঝেন না।,0,politics
চাপাবাজ মহিলা,0,politics
ভাল একটা ভোট করেন কত সীট পেয়ে থাকেন দেখেন।,0,politics
আংলিগের সাধারন সম্পাদকের পদে জননেতা তোফায়েল আহমেমদ কে চাই,0,politics
আর টপিক পাইনাই!,0,politics
বাংলাদেশের পরিণতি ভয়াবহর দিকে ঠেলে দিছেছ আওয়ামীলিগ,0,politics
খালেদা জিয়া হচ্ছে দেশ নেত্রী ।আর কাদের হচ্ছে প্রতি বন্দি কমেডিয়ান,0,politics
আরে কাওয়া কাদের হিন্দুর পোজাইয়া লাগে আর হাছিনারে দেবি দুরগা মা বানাইছে খালেদা তো কিছুই করে নাই মালাই য়ন কি জবাব দিব এ ছাড়া,0,politics
খালেদা জিয়ার সাথে ওবায়দুল কাদেরের তুলনা করটা দলকানা করা আওয়ামী চামচাদের কাজ,0,politics
ট্রাফিক পুলিশের সতর্ক হতে হবে আরো।,0,politics
এগেয়ে জান মিনা ফারহানা,0,politics
সোহেল তাজকে দিলে ভাল হবে,0,politics
ইনুর টার বেশি ভোট নাই,0,politics
জয় বাংলা জয় কাদের কাকা🤗,0,politics
অাওয়া‌মি‌লিগ এসব কাজ‌জে কর‌ছে কেউ কি ভা‌লো ব‌লে না খাপ ব‌লে অার পু‌লিশ কি ক‌রে এখন নিরব কে‌নো,0,politics
মিতব্যয়ী কখনো অভাব গ্রস্থ হবে না। আল কোরআন,0,politics
অর‌েতো দ‌েখি ড‌িম ফ‌েইকাই মাইরা ফালাইব‌ো কয়দ‌িনের মধ্যে😂😂😂,0,politics
অালহামদুলিল্লাহ,0,politics
খুব শিগ্রই বাংলাদেশ সুদানের মত হয়ে যাবে করার কিছুই নেই। কারণ এটাই অামাদের ভাগ্যে অাছে। তবুও ভাল অামাদের সত তাজা কিছু প্রানের বিনিময়ে ঈশ্বরদীর ভূমি মন্ত্রী অার পুলিশের ডি অাইজির যার বিরদ্ধে এখন নারী নির্যাতন মামলা চলছে যার নাম ধর্ষক মিজানুর রহমান এদের মত কুত্তাদের লাত্তেইয়ে ঘুতাইয়ে গুলি করে মারতে পারবো😡😡😡,0,politics
সালা মিথ্যুক!!,0,politics
খালেদা জিয়া যে এতিমের টাকা চোরি করছে সেটা ধামাচাপা দিতেই এরা এখন নতুন নাটক শুরু করছে।,0,politics
বালের নির্বাচন করতে বলছে কে এখন ছাত্র-ছাত্রীরা হলে ঘুমাতে পারেনা,0,politics
কোথায় রাজ রানী আর কোথায় বুড়ো চোতমারানি আপু আপার কথা সত্যি,0,politics
ভালোলাগে আপনাকে ভালোলাগে আপনার ভিডিও ❤,0,politics
খালেদা জিয়ার পায়ের জুতার সমান ও না ওবাইদুল,0,politics
আজাইরা যতসব। বিনপি এর নেতারা সবচেয়ে বড় চিটার দুর্নিতিবাজ। সালে বাংলাদেশের অর্থনৈতিক অবস্থা কেমন ছিল সবাই জানে। তখনকার আমলে বিদুৎ এর অবস্থা ভাল ছিল না রাস্তা ঘাট ভাল ছিল না!! বাংলাদেশের মানুষ তখনকার আমলে এক্টা কিনার সামর্থ ছিল না একটা মোবাইল কিনার জন্য সৌদি প্রবাসি ভাই এর দিকে তাকিয়ে থাকতে হত!! এখন মানুষ এক্টা মোবাইল হারাইলে আরেকটা কিনতে পারে!!! আগে রোস্ট পোলাও এর গ্রান শুধু সৌদি ইতালি প্রবাসি দের ঘর থেকে আর এখন সবাই কম বেশি মুরগী দিয়ে খেতে পারছে!! আগে পোলাপান রা পকেটে টাকা টাকা থাকত।এখন পোলাপানরা জন্মদিনে বন্ধু দের নিয়ে টাকায় পার্টি করছে!!! আগে ইন্টারনেট ব্যবস্থা ভাল ছিল না তাই জে কোন কিছু জানার জন্য কম্পিউটার এর দোকানে যেতে হত এখন ক্লাস এর বাচ্চাও সব জান্তে পারে!!!!,0,politics
এখন থেকে ডিমের দিন,0,politics
জনাব। ওবায়দুল কাদের।। সালে।।। গৃহভৃতততো র চাকুরি ও পাইবেন না।।। জাইমার।বাড়ীতে।,0,politics
আওমিলীগ ছাড়া নির্বাচন করলে পুলিশ সেনাবাহিনী নির্বাচন কমিশন কারো সাপোর্ট পাবেনা। এটা কি ইনু জানেনা??? কত্তবড় সাহস।,0,politics
সালেও শেখ হাসিনা টি আসনে ফেল করে ছিল।শেখ হাসিনার তোলনা চলে না খালেদা জিয়ার সাথে আর ওবায়দুল কাদের কথাতো প্রস্ন হয় না।,0,politics
অপু উকিল এই সব কি বলছে তারা ভোট চুরি করে সরকার ঘটন করে পুলিশ বাহিনি দিয়ে আবার বড় কথা বলে কি ভাবে,0,politics
অপেক্ষা শেষে নতুন ভিডিও পাইলাম😍😍😍ভিডিও দেখার আগেই কমেন্ট করছিলাম ভিডিও টা সত্য তথ্য অনুযায়ী সাজানো ঠাকুর ঘরে কে আমি কলা খাই না এমনটা হয়েছে । তিনি যদি গিফটই পেয়ে থাকেন তবে নিউজ চ্যানেল বন্ধ করে দিলো কেন? আর কি এমন কাজ করলে বা কতটা ভালোবাসলে লাখ লাখ টাকা মূল্যের ঘড়ি গিফট হিসেবে পাওয়া যায় তা আমরা সবাই জানি। আর একজন মন্ত্রী হয়ে সম্মানী ব্যক্তি হয়ে কেমনে এক মুখে দুই ধরনের কথা বলে বুঝি না।,0,politics
আসলে এসব দিয়ে প্রমাণ করা যাবে না উনি অসৎ অনেকে আছে আমার মতো নিজে যা ইনকাম করে তার চেয়ে দুইগুণ তিনগুন টাকায় সখ পুরন করি।,0,politics
রোজা অবস্থায় আছি এজন্য অপু উকিল কে কিছু বললাম না যাও গিয়ে কাওয়ার বিছানা গরম কর ।,0,politics
আল্লাহ তুমি নূরকে হেফাজত করো,0,politics
ধন্যবাদ আপনাকে।আপনি তো শুধু দেশের কথা ভাবেন। আজ যদি আপনার মতো অন্যরা ভাবতো দেশ আরো উন্নত দিকে এগিয়ে যেত।,0,politics
ওয়াল্লাহি কোন দেশে বসবাস করি একটা কমেন্ট ও বালানায়,0,politics
শিখহাসিনা খমতাই আছে ভলেই নূরু এখনো এই পৃথিবীর মুখ দেখছে অন্য কোন দল যদি খমতাই থাকতো তাহলে এত দিন কবেই নূরু হারিয়ে যেতো,0,politics
কথায় আছে লাভে মানুষ লোহার বোজা ও বয় কিন্তু বিনা লাভে তুলার বোঝা ও বয় না!,0,politics
কাউয়ার বাল,0,politics
লাইট্টাদের দেখলেই মাতাটা 🍴😡,0,politics
তো আপনার এতো জ্বলে ক্যান। 😆,0,politics
এমপি মন্রিরা সবগুলারে চোদে,0,politics
আমার মনে হয় ঢাকা বিশ্ববিদ্যালয়ে কিছু ছাগল ভর্তি হয়েছে,0,politics
ছায়েদ আলম ভাই আপনাকে আনেক আনেক ধন্যোবাদ আমি আপনাকে একটা কতাবলি জে বাংলাদেশে তোআপনারা হচ্ছে ন গোন্যো মান্যো বেকতি আপনারাই তোমুখ বুজে আছেন কারন সারথে জদিবেঘাত ঘটে,0,politics
আলোচনা অনেক ভালো লাগলো সাবস্ক্রাইব করলাম বস্।,0,politics
বুঝতাম পারলাম না ইনু কে সবাই কমেন্টে এতু সম্মান দিতেছে কেন।,0,politics
আমার ঘড়ির দাম মাত্র টাকা। কই টাইম তো ভুল দেখায় না সব ঠিকঠাক আছে।,0,politics
হ্যাঁ মোরা বাংঙ্গালী,0,politics
জয় বাংলা ডিম লীগ সামলা।,0,politics
ফাটা কেষ্ট অবায়েদুল কাদের যদি অঢেল টাকার মালিকই না হবেন তবে আওয়ামী লীগ করবে কেন ? গরীবের রক্ত না চুষে লুটপাট না করে কোথায় কে অঢেল সম্পদের মালিক হয়েছে ভবে ? এ কথা তো সত্য জানে সবে।,0,politics
নুরা দেহি সফেদ পাঞ্জাবী হিন্দা শুরু করি দিসে। ও মনু,0,politics
নুর ভাই এখন নেইমারের চেয়েও ভাল খেলছেন।,0,politics
পরিবর্তন জরুরি,0,politics
অামরা এসব চাই না অামরা চাই দালালমুক্ত বিঅারটিএ,0,politics
ইনু সাহেব আপনি না থাকলে আওয়ামী লীগ এর কিছু হবে না,0,politics
তোমরা কি করো পতিহত করো তাদের এই সন্ত্রাসী ছাত্র লীগ কে পতিহত করতে হবে,0,politics
জাতীয়তাবাদী দল বিএনপি তিন তিন বার সফল ভাবে রাষ্ট্র পরিচালনা করেছে তা কি জানেন?,0,politics
আহারে আমরা একটা জোকার হারাবো,0,politics
আওয়ামী লীগ হাইড্রোর মত ক্ষমতা পেলে গোল গোল ঘরে,0,politics
আমলিগ সব চুর,0,politics
মানুষ কোন মিথ্যা বাদীকে দেখলে বলে তুই লীগ।,0,politics
খালেদা জিয়া নির্ভেজাল ভালো মানুষ সবচেয়ে জনপ্রিয় নেতা যে কোনো সময় নিরপেক্ষ নির্বাচন হলে খালেদা জিয়া প্রধানমন্ত্রী। কাউয়া বিশ্বমানের মিথ্যাবাদী চোরাই সরকারের জন্ম।,0,politics
কাদের তো মিনি মিনি করে কথা বলে কথা বলতে পারেনা৷ কাদের তো জা বলে মানুষ তো বাবে মিথা কথা বলে,0,politics
চাপা বাজের সাথে জননেত্রী সাথে তুলনা করে❓❓❓❓,0,politics
রাজকীয় পরিবারের জন্য এইসব খুব সামান্য।ইমেলদা মার্কোস সহ অন্যান্য রাজকীয় পরিবারের সম্পদের সাথে তুলনা করার অনুরোধ রহিল।,0,politics
বিনোদন 😁,0,politics
জনগনের টাকা।।,0,politics
ভাই তুমি একটু সাবধানে থাইকো।,0,politics
সালা নাটক,0,politics
কোনাই কাও্ওয় কোনায় মানুষ,0,politics
সে সড়ক মন্ত্রী হয়ে ও কি উন্নয়ন করতে পারছে একটা দেশের হাইওয়ে রোড ভালো হলেই কি দেশের সব রাস্তা ভালো আপনি দেখেন বাংলাদেশে হাইওয়ে রোড টা ছাড়া আর এর ভিতর রাস্তার কি ভয়াবহ অবস্থা যদি দেশের ভালো চান তো এগুলা বাংলাদেশের রাস্তা না এগুলা ভালো করেন?,0,politics
কাদের কাকু নাকি,0,politics
ভি পি ভাই আপনাহদের কি হাত নেই ওদের বিছার কেউ করতেপারবেনা আপনারাই করতে হবে আপনাদের বিছার,0,politics
কোনদিন নাযানি শুনি নুর ভাইকে মাইরা ফালাইছে আল্লাহ জেনো হেফাজত করে,0,politics
চোরের মার অনেক বড় গলা,0,politics
প্রশাসন এগুলো পরিচালনা করে,0,politics
বা লার ছাএ তগো কি কমু তরা লেখা পরার নামে সন্তাস করছ তরা ভাল না,0,politics
আপনার ড্রাইভার লাইসেন্স আছে ত,0,politics
ভাল বলে,0,politics
পগলের প্রলাপ,0,politics
কার সাথে কি ফেনে ভাতে ঘি,0,politics
বিচারহীন দেশে ভালো কিছু প্রত্যাশা করাই ভু,0,politics
সব চেয়ে দুনিতিবাজ ওয়বাদুল কাদের অাওয়ামিলিগ সব চেয়ে দুরনিতিবাজ,0,politics
সাহেদ ভাই অনেকে দিন পর আপনার ভিডিও দেখলাম,0,politics
কোথায় সেকসাধী কোথায় বরকির লাদি,0,politics
আমরা মনে লেখা পড়া শিখার চেয়ে আৃাদের সন্তানদের অশিককিত রাখা ভাল। কারন কোথায় শিখবে লিখাপড়া।,0,politics
আপনাকে সাধুবাদ জানাই। সেই সাথে সাবধানে থাকবেন ভাই।,0,politics
মনে হয় বছরের আগের টাকার গোলমালের,0,politics
ফাটাফাটি,0,politics
যে লোক তাকে এতো টাকার জিনিস উপহার দেয় সেই লোকের লাভ কি তা কি সবাই জানে আসলে এই গুলি এই ধরনের দুর্নীতি,0,politics
সরকারের দালালি আর কত করবি।,0,politics
আমরা সবই বুজি 🤣,0,politics
বাজেট নিয়ে কথা দেখ জনজন এই বছরে যত টাকা বাজেট হয়েছে! তার থেকে বেশি টাকা বাজেট হলে ও দেশ সান্তিতে চলবে যুদি সরকারের দলের লোক দুর্নীতি বন্ধ করে !!,0,politics
আপনার কথা জনসাধারন বিশ্বাস করে বলে মনে করেন?,0,politics
কোথায় মহাখালী আর কোথায় জুতার কালি,0,politics
ইসলামিক ভিডিও পেতে আমাদের চ্যানেল টি ঘুরে আসুন,0,politics
ওই মহিলা পাগল হয়ে গেছে গা বিএনপি ক্ষমতায় এসে এক সালে তিন শালে না পাগল হইছে পাগল,0,politics
মাত্র টাকা দামের একটা ঘড়ি আজ বছর ধরে এমাজন এ দেখে দেখে মনের আশা পুরন করছি আর সালা দেখো,0,politics
সেলফি তোলার জন্য রাস্তায় নেমেছে,0,politics
বুড়ী তো শেখ হাসিনাও তাইলে উনি থাকবে কিভাবে। 😂,0,politics
হায়রে আমরা কত কষ্ট করে চেকচ দিয় আর এরা এত টাকা দিয়ে ঘডি পরে পেলতেচে হারামি জালিম আল্লাহর গজব পডুক,0,politics
আওয়ামীলিগের জন্য 🖕🖕🖕,0,politics
রুমি ফারহা অনেক বেদপ ।,0,politics
টাকার ঘড়িইতো বেশি মনে হয় আমার কাছে।,0,politics
এমন লীগ রে ধরে ধরে ডাস্টবিনে ছুড়ে মারো,0,politics
প্রথমত মন্ত্রণালয়ের নাম অজানা কেউ একটা কাগজে লিখে দিলেন আর একটা অনলাইন পোর্টাল সেটা নিয়ে সংবাদ তৈরী করা হলো আর আপনি সেটা ধরে একটা বোমা ফাটিয়ে দিলেন। ওবায়দুল কাদেরের কমপক্ষে টি বই অনলাইনেই পাওয়া যায়। আর আপনি কিছুই জানেন না!! কিছু দিন আগে বললেন সরকার চীনের দিকে ঝুকে গেছে এখন বলেন ভারতের কাছে নতঝানু পররাষ্ট্রনীতি। আপনি পারেনও বটে। শেখ হাসিনা না থাকলে বুঝতেন!! ঠেলা কারে কয়??,0,politics
তুই ইনু জিবনে মন্ত্রী হইতে পারতি? শেখ হাসিনা তর বাবার কাজ করছে! তুই সুযোগ পাইলেই আওয়ামীলীগের খতি করবি!!,0,politics
আমার বাড়ি ময়মনসিংহ ফুলপুর নং ইউনিয়নের ছনধরা গ্রামের কেলোমিটার রাস্তা বছর দরে করতেছে এখন কাজ ব্ন্ধ আছে জানিনা কবে,0,politics
এইটা কোন মানুষের কাজ না আল্লাহ তুমি রক্ষা করেন,0,politics
তাহসিন এর হেটার গুলা কই সাড়া দাও,0,politics
হায়রে আমার সোনার বাংলা😰,0,politics
জমির জামি ন্যায় নীতির রাজনীতি করে বলেই সত্যকে সত্য বলতে পেরেছে আর যারা দালালির রাজনীতি করে তাদের পক্ষে সত্য কথা বলা অসম্ভব ৷ ওবাইদুল কাদেরের মত লোক দলের জন্য কথটা ক্ষতিক্ষারক সেটা দল ক্ষমতাচ্যুত হলেই বুঝা যাবে আর ইসতিয়াকদের মত নেতারা দালালি করে দলে টিকে আছে কিন্তু আর কতো দলালালি একদিন এই দালালির শেষ হবেই ৷,0,politics
ইয়াবা কাদের,0,politics
রুমিন ফারহানা একটু দম নিয়া নেন তা না হলে তো স্ট্রক করে মারা যাবেন।,0,politics
ইনু চাটুকারিতা চালিয়ে যাও সামনে আসছে সুদিন,0,politics
কাদের স্যার আমার কুপ পিয় মানুস,0,politics
সুবিধা দিয়ে এমপি আর হুইপ বানাই দিছেন।এইটা কি করবেন?,0,politics
চাতকের মত চেয়ে থাকি ভাই ভিডিওর জন্য।,0,politics
জাসদ তোমরা আফগানিস্তানে যাও,0,politics
আমার চ্যানেল টা সাবস্ক্রাইব করুন।,0,politics
সালি কই তেকে এলো আমার মনে হয় বসতি তেকে এলো নাকি,0,politics
সাহসী,0,politics
বাংলাদেশের মানুষই জানে সবকিছুই কারণ স্বৈরাচারী আওয়ামী লীগ না বিএনপি সেটা আপনাকে বলে দেওয়া লাগবে না,0,politics
"যাক,এতো সাহসি একটা লেখা দেবার জন্য অসংখ্য ধন্যবাদ।",0,celebrity
অসাধারণ।,0,celebrity
কমেন্ট পড়তে আসলাম ✋✋,0,celebrity
দালাল। ভাওতা বাজ।,0,celebrity
এই টুমি এত এট ডুষ্টু ক্যানু? -_-,0,celebrity
"আমি কমেন্ট পরছি য়াঢ় ফ্রুসুর পরমানে হাসছি,r গফ কে আদর করতেছি।",0,celebrity
"লেখার কনস্ট্রাকশন কিভাবে একই রকম রাখেন? এক গ্লাস পানি খান, বমির পর এটা ভালো লাগার কথা।",0,celebrity
ব্রেকিং নিউজ!!  স্যার ১৫ ঘন্টা আগে চান্দের দেশ থেকে  বাংলাদেশে এসেছেন🐸🐸,0,celebrity
পোস্ট করতে না করতেই বাচ্ছারা কমেন্ট করতে শুরু করে দিছে। ভাল্লাগছে ।,0,celebrity
অমিত বাড়ৈ,0,celebrity
"স্যার এখন কেমন বোধ করছেন?  বমি কি বন্ধ হইছে? নাকি এখনো হড়হড় করে বমি করছেন? সুপারি খান,  সুপারি বমি বন্ধ করতে উপকারী। পোলাপনদের কথায় কিছু মনে করবেন না!  ওরা অবুঝ। আর বাকিরা জামায়াত-শিবির :D",0,celebrity
গরুর রচনা,0,celebrity
"আপনাকে সরাসরি দেখার সৌভাগ্যটা আমার হয়েছে চুয়েটে একটা পরীক্ষার দরুন,। আপনি আমার সার্টিফিকেটেরর পেছনে সাইন করেছেন,,,, আমি সেটা সযত্নে রেখে দিয়েছি,,,আমার পড়ার টেবিলের উপরে সার্টিফিকেট টার উল্টো পৃষ্ঠাটা রেখেছি যেটাই আপনার সাইন করা,,,  আপনার উপর হামলার ঘটনা শুনে খুব খারাপ লাগছিলো এই ভেবে যে হয়তো ১৪ই ডিসেম্বর আবার ফিরে এসেছে,,,  ঈশ্বরের কাছে প্রার্থনা করি যাতে তাড়াতড়ি সুস্থ্য হয়ে আবার আমাদের ভালো লিখা উপহার দিবেন।। ♥♥",0,celebrity
"প্রটোকল ছাড়া বের হইয়েন না রাস্তায়, দেশের শতশত পোলাপান হড় হড় করে বমি করে দেবে আপনার গায়ে :)   যতই রঙ মাখানো লেখা লেখেন আপনার ""ক্ষমতার পা-চাটা"" চরিত্র জাতি বুঝে ফেলেছে ... :)",0,celebrity
"তোমার চেতনার দন্ডে লাথি মারি এদেশে কোটি যুবক আপনার মত দালালির জন্য মুক্তিযুদ্ধ এর চেতনা লালন করেনা, আর কত পা চাটবেন শুনি?",0,celebrity
"এক সময় ২১ বই মেলায় যেতাম শুধু আপনার আর হুমায়ুন স্যার এর বই সংগ্রহ করতে। আপনার সাইন্স ফিকশন গল্প গুলো পড়ার সময় মনে হত, স্পেসশিপটার ক্যাপ্টেন আমি, আবার অনন্তকাল লাইফ সাপোর্ট এ থাকা ঘুমন্ত মানুষটাও আমি। এলিয়েনদের সাথে আর রোবটিক্স যুদ্ধগুলোও আমি করে জয়ী হয়েছি। যখন বয়স আমার ১৪ তখন বাবা আমাকে আর আমার বোনকে আপনার দুটি বই দিয়েছিলেন, আমাদের জন্নদিনের উপহার। সেই থেকে আপনি আছেন আমাদের সাথে। আজ আমার বয়স ৪৭, আর আমার সেই বোনটি মাত্র ৪৮ বছর বয়সে ২০১৬ তে আমেরিকার টেক্সাস এ জামাই সহ রোড এক্সিডেন্ট এ মারা গেল। এত কথা কেন লিখলাম তাই না? কারন, আপনার বই এর দিকে তাকালে আমি এখনো আমার বোনটার সেই হাসি মাখা মুখটা দেখি যেটা সে হেসেছিল আপনার কপোট্রনিক সুখদুঃখ বইটা হাতে নিয়ে। আমার কিচ্ছু যায় আসে না, আপনি নাস্তিক নাকি আস্তিক। আমি এতটুকুই জানি, আপনি আমার আর আমার বোনের মুখে হাসি ফুটিয়েছিলেন। হুমায়ন স্যার এর সাথে আমার অনেক কাছের সময় কেটেছে প্রয়াত সাদিক ভাই  (হুনায়ুন স্যারের নাটকের অভিনেতা) এবং প্রক্ষাত গায়ক নিয়াজ মোহাম্মদ সাহেবের সাথে ঘনিষ্ঠতার কারনে। অনেক আসরে অনেক সময় কাটিয়েছি। সেই রকম সউভাগ্য আপনার সাথে কাটানোর সুযোগ আমার হয় নি, তাই একটা ক্রাইসিস থেকেই গেল। দোয়া করি, আল্লাহ অবশ্যই আপনার মঙ্গল  করবেন।",0,celebrity
নামাজ পড়ার জন্য ওজু করে ফেলাতে অশীল্ল ভাষায় তোর মতো দালাল কে গালী দিতে পারলাম না।,0,celebrity
"স্যার,আপনার সুস্থতা কামনা করি।",0,celebrity
"কি পোস্টে কি কমেন্ট,,, যারা কমেন্ট করছে তাদের বেশীর ভাগই মনে হয় জামাত শিবিরের লোক,,,পয়সা খেয়ে কমেন্ট করতে আসছে,,,,ছিঃ",0,celebrity
"Sir, Public exam গুলো আমাদের জন্য সবসময়ই মানসিক চাপের । স্কুল থেকে শুরু করে বাড়ি অব্দি তো দেয়া হয় বটেই , নিজের প্রতি নিজের মধ্যেও যেন কেমন একটা চাপ কাজ করে...... যে চাপটা আগে নিতে হতো দশম শ্রেণিতে , এখন তা অষ্টম এমনকি পঞ্চম শ্রেণিতেও নিতে হয় ! ছোটদের জন্য এ ভারটা খুবই কষ্টকর..............এটা বন্ধ হলে আমরা যেমন চাপমুক্ত হবো, তেমনি প্রশ্নফাসও হবে না ¡",0,celebrity
"কাজে কর্মে থাকি,এত বড় স্ট্যাটাস পড়ার টাইম ক‌ই...🚶",0,celebrity
জনাব নিজের ভোট টা দিতে পেরেছেন? নাকি ভোট চোরদের কে সুযোগ  দিয়েছেন?,0,celebrity
"মুহাম্মাদ শাহজালাল, BD Nayem Durjoy, Tamjid Hossain, Sabbir Ahmed, Md Hossain Ahmed Roomman, Rakib Islam Shakib, Mamdud Talukdar, Masum Billah, Khan Jahan Rimon, S.m. Rabiul Islam Mon kharap thakle comments gula porte paren",0,celebrity
ঘুম কি ভেঙ্গেছে ওহে বুদ্ধিজীবী???,0,celebrity
"স্যারের ভোর এখন হয়েছে বুঝি  ??  ঘুমিয়ে পড়েন স্যার,যখন সকাল হবে আমরা আপনাকে জাগিয়ে দিব ।",0,celebrity
"বিমানের জানালার পাশে বসে হাওয়া খেতে খেতে উগান্ডা যাচ্ছিলাম আর মোবাইল গুতাগুতি করছিলাম।   হঠাৎ এই পোস্টটা আমার চোখে পড়ে। পোস্ট টা দেখে আবেগের চোটে আমার মোবাইলটা পড়ে গেল।  কিন্তু আমাকে তো HaHa react দিতে হবে।জীবনের মায়া ভুলে লাফ দিলাম মোবাইল এর পিছে। ৫ মিনিট উড়ার পর উত্তর বিষুব রেখা বরাবর ৪৫ ডিগ্রি অক্ষাংশে ভূ-তাপীয় অঞ্চলে এসে মোবাইল এর নাগাল পাই।  সাথে সাথে পোস্ট এ HaHa react দিয়ে দিলাম। এখন শান্তি লাগতেছে। এখনো নিচের দিকে পড়তেছি। নিচে সাগর দেখা যাচ্ছে। সাগরের হাঙ্গর হা করে আছে আমাকে খাওয়ার জন্য। আমি মনে হয় আর বাঁচবো না, কিন্তু কোনো আফসোস নেই আমি পোস্টে HaHa react দিতে পেরেছি!😛",0,celebrity
স্যার আমি আপনার পোষ্টের কমেন্ট পড়া ফ্যান.... এখন কমেন্ট গুলা পড়বো সময় পেলে কয়েকঘন্টা পর আবার এসে পড়ার চেষ্টা করবো। হাসি-খুশী থাকলে শরীরের জন্য ভাল।,0,celebrity
লেখায় বুঝতে পেরেছি যে আপনিও গুম হয়ে যাওয়ার ভয়ে আছেন,0,celebrity
তোর না মন খারাপ ?পড় ভালো লাগবে! জাফর স্যার এর পোষ্ট এর কমেন্ট বলে কথা  নিঝুম রাতের চাদ,0,celebrity
পুরা পোষ্ট টা পড়লাম। সাহিত্যিক দিক থেকে খুবই উন্নতমানের লেখা। তবে কথা হইল এতদিন পড় উনার ঘুম ভাঙায় হাহা রিয়েক্ট দেয়া ফরয হয়ে গেছে। তাই আমিও একটা হাহা রিয়েক্ট দিয়া দিলাম,0,celebrity
"স্যার, শুধু একটা বার কমেন্টগুলা পইড়া যান প্লিজ😄",0,celebrity
বমি😜😜😜,0,celebrity
"এখানে যারা এরকম পোস্টে হাহা দিতে পারল, আবর্জনা মার্কা কমেন্ট করল,, ওরা মুন্ডে ব্রেইন নয় আবর্জনা ধারণ করে মাত্র।মানসিক রুগী ও বটে, দেশের ভালো তো চায়না বটেই।আর যেগুলায় বলে পোস্ট নয় কমেন্ট পড়তে আসছে বলে কমেন্টালো ওগুলা বলদ।",0,celebrity
ওয়ার্ল্ড কাপ তো আর সাত দিন পর শেষই হয়ে যাবে!!!! পারলে বাংলাদেশের কোটা সংস্কার নিয়ে লিখুন,0,celebrity
"লোকটা ঘুমে থাকে, তার হিসাব থাকে না।",0,celebrity
"স্যার শহীদুল আলমের মতো আপনার অবস্থা হবে না।কারণ আপনি যা পারেন শহীদুল আলম সেটা পারে না।তাই তো তিনি আজ জেলে, পুলিশি নির্যাতনের শিকার আর আপনি কি চমৎকার বহাল তবিয়তে আছেন।  আর কোন গুলোকে গুজব বলছেন?তথাকথিত ""একদল যুবক"" যারা হামলা করছে ঐ গুলোকে??সাংবাদিকদের ওপর হামলার তথ্য প্রমাণকে??আর হামলা করতে গিয়ে আহত কর্মীকে সাধারণ সম্পাদক ও সভানেত্রীর দেখতে যাওয়াকে??তাইতো বলছি,শহীদুল আলম আপনার মতো না।তাই ওনি জেলে।",0,celebrity
ইনি এতো উত্তেজিত হয়েছেন কেনো বুঝতে পারছিনা। এনার তো চুপ থাকার কথা।,0,celebrity
"আমাকে কেউ একটি পজিটিভ রিপ্লাই খুজে বের করে দাও, এত্তবড় বিজ্ঞানীরর জন্য কোন পজিটিভ রিপ্লাই খুজে পাচ্ছি না কেন?",0,celebrity
"স্যার বেঁচে আছেন?? না কি স্যারের আত্মা কথা বলছে?? স্যার বেঁচে থাকলে এতোদিন পর কথা আসতোনা!! স্যার ফেবু চালান না তো কি হয়েছে?অন্যান্য গণ মাধ্যমেও স্যারকে পাওয়া যায়নি!! কোন পত্রিকায় স্যারের দু লাইনের একটি কলাম ও দেখা যায়নি!! বাহ স্যার!!বাহ!! আমাদের এলাকায় পুকুর সেঁচে সব মাছ ধরে নিয়ে যাওয়ার পরও কিছু মানুষ মাছ ধরতে আসে!!আপনাকেও তেমন মনে হচ্ছে!! অনেকটা এমন স্যার,যেন রোগী মারা যাওয়ার পর ডাক্তারের আগমন!! স্যার এসব ভাড়াটে সিম্প্যাথী আমরা চাইনা!! ওপারেই ভালো থাকুন!!",0,celebrity
"জামাতি,বামাতি তোদের মারে লটকাই এত সো।দার পরেও কি শিক্ষা হয় না",0,celebrity
আচ্ছালামুয়ালাইকুম স্যার। আশা করি ভাল আছেন। আমি আপনার  সাথে  মাধ্যমিক  তথ্য ও যোগাযোগ প্রযুক্তি পাঠ্য বইয়ের কিছু বিষয় নিয়ে কথা বলতে চাই।,0,celebrity
"@muhammed zafar iqbal স্যার বঙ্গবন্ধু কি নিজে নিজেই জন্মিয়েছেন, না কি সৃষ্টিকর্তা বলে কেউ একজন আছেন যিনি যেই সময়টিতে বাংলাদেশের মাটিতে তার মত একজন নেতার দরকার হয়েছিল সেই সময়টিতেই তার জন্ম হয়েছিল। প্রশংসা যদি করতে হয় সৃষ্টিকর্তারই করা উচিৎ। তিনিই সকল প্রশংসার দাবীদার।",0,celebrity
"একজন শিক্ষক হয়েও আপনার কাছে এমন পোস্ট কল্পনাতীত ছিল। সবাই বলে আপনি নাকি তেলবাজি করেন। কিন্তু সেটা ভুল প্রমাণ করলেন। অন্যান্য অধিকাংশ শিক্ষকরাই মৃত অরিত্রীর উপর দোষ চাপাচ্ছে শিক্ষকদের বাঁচানোর জন্য। কিন্তু আপনি সত্যিটা বলেছেন। শিক্ষক হয়েও শিক্ষকের পক্ষ নেননি। আপনিই শিক্ষকের মর্যাদা পাওয়ার যোগ্য। Salute, sir...",0,celebrity
ভাই আমার কিছু কবানি? Mainka Cipa,0,celebrity
দেওয়ালে পিঠ ঠেকে গেছে অথচ প্র্যাকটিকাল খাতা এখনো আঁকা এবং লেখা হয়নি?পরীক্ষার আর বেশিদিন বাকি নেই?পড়াশোনা এবং প্র্যাকটিকাল খাতা আঁকা ও লেখা নিয়ে হিমশিম খাচ্ছেন? কোন সমস্যা নাই।আমরা আছি কিজন্য?যোগাযোগ করুন-01791643953 এই নাম্বারেে। . [বি.দ্র-আমরা এখনো হাত অত লম্বা করতে পারিনি বিধায় চট্টগ্রামের বাইরে কাজ করতে পারছি না।অতএব শুধুমাত্র চট্টগ্রামের শিক্ষার্থীদের জন্য করতে পারছি।তবে কেউ যদি কুরিয়ার খরচ দিয়ে করাতে চান সেক্ষেত্রে দেশের যে-কোন প্রান্তের কাজ করে দিতে পারব।],0,celebrity
আপনার মত মেধা বাংলাদেশে সবসময় প্রয়োজন ।। কিন্তু দুর্ভাগ্য একটা অন্ধ অবুঝ দল আমাদের এই মহামূল্যবান মেধাবী লোক গুলোর ধ্বংস করতে মরিয়া হয়ে উঠছে ।। আপনি ভালো থাকুন স্যার ।,0,celebrity
"@Hossain Emon >>  জ্বি, বিরাট ধার্মিকের মুখের ভাষা শুনতে বড়ই সুমধুর...",0,celebrity
মুক্তিযুদ্দে না যেয়ে যিনি পালিয়ে বেরিয়েছেন......হাহাহা... ভালো ই তো  দেশপ্রেমিক,0,celebrity
স্যার আপনি দ্রুত সুস্থ হয়ে উঠুন।,0,celebrity
লেখাটি পড়ে মনে হচ্ছে অতি সুনিপনে এই বীজ আপনার পশ্চাৎদেশ দিয়ে ঢুকিয়ে দেয়া হয় কয়েকদিন পরপর। আর বাচ্চা গর্ভে ধারণ করার আদলে এসব বীজকে 'সম্মুখদেশের' অভাবে আপনি 'লেখা' আকারে হাত দিয়ে বের করেন। ভাগ্য ভালো  আপনার সেই 'সম্মুখদেশের' অভাব। নাহলে 'গুমলীগের' জারজ জঙ্গীতে সয়লাব হতো পুরো দেশ।,0,celebrity
স্যার আমি জানতাম আপনি গর্ত থেকে বের হবেন! তাই রাস্তার হকার থেকে ইঁদুর মারার ঔষধ কিনে রাখছি।,0,celebrity
আল- আমিন আলমগীর হোসাইন,0,celebrity
"স্যার আপনার মত করে কয়জন ভাবে ,,,,,অামাদের শিক্ষা ব্যবস্থাই যেন কেমন হয়ে গেছে ,,,,,ছেলে মেয়েরা যদি ক্লাসে না আসে এটিতো আরো ভয়ংকর,,,,,",0,celebrity
স্যার আপনের লেখাটা ১০০% দায়সারা ঘোচের। আমার খুবই আনন্দ লাগছে এই ভেবে যে সবাই আপনার ভন্ডামী ধরে ফেলছে। এবং ইচ্ছেমত সবাই আপনার গায়ে হড়হড় করে ভমি করতেছে।,0,celebrity
বড়ভাই চলে আসেন চরম বিনোদন। Asikur Rahman,0,celebrity
"স্যার,আপনি অসুস্থ। বেশী জানতে গেলে হজম করতে পারবেন না। আপনার কিছু হলে বা আপনি চলে গেলে আমরা কার কাছ থেকে ড্রোন বানানো শিখবো??",0,celebrity
"আপনি বাপু সুসময়ের কোকিল!কাজের বেলায় চুপ করে ঘাপটি মেরে লুকিয়ে থাকেন,আর কাজ পুরালে আপনি পাজি সাহেব সাজেন.",0,celebrity
আর্মি অধ্যুষিত এলাকায় সবই সম্ভব।  এটা কে তার ভাবছে তাদের আভিজাত্যের বহিঃপ্রকাশ।,0,celebrity
বুঝলাম...........এ নয়া সরকারের আমলে ঘন ঘন গর্ত থেকে বের হবেন আর  গন্ধ ছড়াবেন।,0,celebrity
কমেন্ট পড়তে আসছি😇,0,celebrity
বি:দ্র: বৃষ্টির কবলে স্যারের বাড়ির ওয়াইফাই লাইনে সমস্যা ছিল যার কারণে যথাসময়ে স্ট্যাটাসটা পাবলিশড করতে পারেননি। ধন্যবাদ।😌,0,celebrity
"কমেডি জগতে আপনার কোন তুলো নাই, আমাকে হারুন কিচিন্জার, হানিফ সংকেত,  হাসাতে পারে নি, কিন্তু আপনি সেই অসাধ্য সাধন করেছেন!!! বড় মায়া হয় আপনার জন্য,  এও তৈল মর্দনের পরও আজ ও সোনার হরিণ মন্ত্রী হতে পারলেন না! আশা ছাড়বেন না,  এগিয়ে যান!!",0,celebrity
বিগত ৫ দিন বসে সে লিখছে।😂😂😂  Imtiaz Imtu,0,celebrity
আমি বিশ্বাস করতে পারছিনা যে আপনি বেচে আছেন। আমি ত শুনলাম আপনি মারা গেছেন। এটা শুনে জানাযার জন্য প্রস্তুতি নিচ্ছি,0,celebrity
",কিছুইতো হচছে না !!!! কি করবেন মা বাবারাই তো আসল হোতা !!!!",0,celebrity
সব কমেন্টে স্যার এর কোন ফলোয়ার কে না পেয়ে আমি হতাশ।,0,celebrity
স্যার মনে হয় বাকিটা জীবন মার্কেটলেস থাকবে..... স্যার কখনো স্বপ্নেও কল্পনাই করেনি যে ওনার চেতনার শেয়ারটা মার্কেটে এইভাবে লস খাবে।। #Stand_for_sir,0,celebrity
লেখার দরকার তাই লিখলেন তাই না স্যার?,0,celebrity
"আপনি আরো অনেক বছর বেছে থাকুন,অনেক কিছু এই দেশটার জন্য দিয়ে যান।",0,celebrity
"আল্লাহ,আল্লার রাসুলকে এবং প্রিয় ধর্ম ইসলাম কে কোনো কুটক্তি করলে বাংলার জমিনে কোনো নাস্তিকের জায়গা হবে না।",0,celebrity
"""স্বপ্ন দেখানোর মানুষের বড় অভাব,আপনার মত যে ক'জন  আছেন,তাদের সংখ্যা ও যদি কমে যায়,আমরা তো স্বপ্নহীন যান্ত্রিক রোবটে পরিণত হবো স্যার""।",0,celebrity
"ভাউ, সারা রাত রামায়ণ পড়ে সীতার মাকে এটা বলতে পারলেন!!! 😆 😆 😆",0,celebrity
স্যার এই কলাম লেখার আগে মদ খেয়েছিলেন তো? আপনি দেশের সবাইকে মদ খেতে বলুন। ওরা মদ খাক আর আপনার কলামে কমেন্ট করুক,0,celebrity
আপনিতো আওমী সুবিধাভোগী তথাকথিত বুদ্ধিপরগাছা।,0,celebrity
আপনাকে মন্ত্রী হিসেবে দেখতে চাই।,0,celebrity
পল্টিবাজ,0,celebrity
"স্যার, ছাত্রদের ন্যায্য আন্দোলনে আপনাকে খুব দরকার। আপনি চুপ কেন?",0,celebrity
"আপনার রচনা মার্কা পোস্ট কখনো পড়া হয় না, আমি আসলে পোস্টের কমেন্টগুলো পড়ি",0,celebrity
"মানুষ মরে যাওয়ার পরেও যে এইভাবে প্রতিবাদী হয়ে ওঠার চেষ্টা করে আমি জানতাম না, ওপারে ভালো থেকেন জনাব 🙊",0,celebrity
পাঁচ বছর পাঁচ বছর করেন কেন? মহাজোট ৯৬% ম্যান্ডেট নিয়ে এসেছে। পাঁচ বছর পর আবার মহাজোট সরকারের অধীনে ঠিক এবারের মত শান্তিপূর্ন এবং সুষ্ঠু  নির্বাচন হবে। সেই নির্বাচনে ইনশাল্লাহ আবার মহাজোট আসবে। তার পাঁচ বছর পরে আবার সেই মহা মহাজোটের অধীনে আরেকটা নির্বাচন... তারপর আরেকটা নির্বাচন...তারপর আরেকটা। সো... আপনার মত আশাবাদী মানুষের মুখে জাস্ট পাঁচ বছর শব্দ মানায় না...বলুন কেয়ামতের আগের দিন পর্যন্ত।,0,celebrity
"স্যার, আসুন। নামায পড়ি।",0,celebrity
বঙ্গবন্ধুর নাম বেচে খাওয়া ছাড়া আর কী করতে পেরেছে বর্তমান সরকার? এই বিষয়টা নিয়েও কিছু বলুন।,0,celebrity
"সরি মিষ্টার, ১৯৫২ তে আমাদের ওটা ভাষা আন্দোলন ছিলোনা, ছিল রাষ্ট্রভাষা আন্দোলন। দাবী ছিল রাষ্ট্রভাষা বাংলা চাই। আর কত ইতিহাস বিকৃত করবেন? শিক্ষিত মানুষ আপনারা, একটু লজ্জাও নেই নাকি? ভাষা আন্দোলন আর রাষ্ট্রভাষা আন্দোলনের পার্থক্য আপনার মত কাউকে শিখাতে হবেনা নিশ্চয়ই???",0,celebrity
মানির মান জুতা দিয়া পিডাইলেও যায় না!!,0,celebrity
আগে যখন টিভি দেখতাম তখন মাঝেমাঝে বাংলা সিনেমা দেখা হতো। বাংলা সিনেমার একটা কমন সিন হলো নায়ক-নায়িকা এক্সিডেন্টে মাথায় বাড়ি খেলে স্মৃতিশক্তির হারায় ফেলে।  আর আজ স্যারকে দেখছি মাথায় ছুঁড়ির ছেচা খেয়ে স্মৃতিশক্তি যা আছে তা তো বিলোপ হইছেই বুঝা যাচ্ছে........ নিজেও এখন কি বলবে না বলবে কোনো দিশকুল পাচ্ছেনা। তাই এখন এসব টাল্টি-ফাল্টি হথা গুলা বলতেছে 🐸🐸  হথোদিন ফর ফর এই ফেসবুকত মাইনসের একেক ঠশা দেহি আমি ছাফ ধরো হয়ে যাই 😱  শিশু সাহিত্য লিখতে লিখতে মন ইয়োনো শিশুর নান অইগেয়িদেনা যে হনো হথা হনো বাছ-বিচার ছাড়া মুখোদি জিয়েন আইয়ি ইয়েন ছটছট মুখোদি হই ফেলনদেনা স্যার 😩  এহন তো জাফর স্যার তারারে নামাজ-কালাম অর হথা হইথামও ডর লাই.... কেউ যদি আবার আর ফিছোদি ছুড়ি ভোয়াইদে বাজিরে বাজি আঁই এন্ডে নাই 😒 😒,0,celebrity
"অভিজিৎ রায় ঠিক কি করছিলো যার জন্য তাকে খুন করা হল, কেউ আমাকে বলবেন দয়া করে ?",0,celebrity
"একটু ভাবুন স্যার!আপনি এ দেশের স্বনাম ধন্য শিক্ষাবিদ।সবাই আপনাকে চিনে, কিন্তু প্রত্যেকে ঘৃণা করার জন্যই চিনে। মুক্তিযুদ্ধের সাফাই গাইছেন!  কিন্তুু মুক্তিযুদ্ধে আপনাদের কোন অবদানই  নাই।",0,celebrity
"স্যার দালালী ছাড়ুন... ""আমি রাজাকার"" ছাত্ররা মতিয়া চৌধুরীকে ট্রল করার জন্য লিখেছিলো, সেইটা খুব ভালোভাবেই জানেন আপনি। তারপরেও দালালী করার জন্য খুব ভালোভাবেই উপস্থাপন করেছেন। মতিয়া চৌধুরী সংসদে দাঁড়িয়ে যখন আন্দোলনকারীদের সবাইকে যখন রাজাকার বানিয়ে দিলেন, তখন তো চুপ দিলেন।  নিজেরাই সাধারণ ছাত্রদের রাজাকার বানিয়ে দিলেন, তকমা লাগিয়ে দিলেন, আবার নিজেই বমি করার কথা বলছেন......  রাজাকার দের সবাই ই ঘৃনা করে, মুক্তিযোদ্ধারা আমাদের দেশের সূর্য সন্তান, তাদের সম্মান সবসময় ই সবার উপরে। কিন্তু কোটা দিয়ে সম্মান দেখানো যায় না। তাদের বেতন ভাতা বাড়ায় দিন, ফ্ল্যাট বানিয়ে দিন। দেশের মানুষ খুশি হবে। কিন্ত চাকরি দিয়ে অন্যের অধিকার কেনো নিবেন। আর আপনার এই দালালির জন্য আপনার উপর বমি করলাম...👎",0,celebrity
"আপনি ভালো থাকুন স্যার , বেশি করে লিখুন এবং এটাও কম আনন্দের নয় আমাদের জন্য। গুণীদের মর্ম বোঝার ক্ষমতা সবার থাকেনা।",0,celebrity
কবু তোমাদের মন খ্রাপ হলে বিলম্ব না করে চলে আসবা!  Sumaiya Islam Nizum HM Ariyan Rakib Kamrul Islam MD Ashdujjaman Tuhin,0,celebrity
"আপনি নিজেও তো রাজাকারের নাতী! এজন্য নিজে কি ঘৃণা করেন? কাদের সিদ্দিকী বলেছেন, আপনার বাবা মুক্তিযোদ্ধাও নয় শহীদ নয়। '৭১ এ তার বোকামীর জন্য নিহত হয়েছেন! আপনাকে বলা হয় গর্তযোদ্ধা...",0,celebrity
আগের পোস্টের কমেন্ট পড়ে শেষ করতে পারিনাই।এরিমধ্যে নতুন পোস্ট।বাহ।,0,celebrity
কমেন্টে_এর 'চোদনে' তোর পেইজ আজ নীল থেকে লাল হয়ে যাবে__😂😂,0,celebrity
প্রিয় স্যার ভালো হয়ে ফিরে অাসুন অামাদের মাঝে সেই চিরচেনা হাসি মাখা মুখটা নিয়ে।এই সুন্দর পৃথিবীটা অারোও সুন্দর করার জন্যে অাপনাদের মতো সুন্দর মনের মানুষ গুলোর যে খুবই দরকার। #Get Well Soon Sir♥♥♥,0,celebrity
"ভান করা একটা অভিনয়, উনি যে রকম ভান করছেন, নেইমার উনার কাছে কিছুই না,সালার ভণ্ডামির একটা সীমা থাকা দরকার...",0,celebrity
এটা কি নাটক? নাকি অভিনয়? একটা ছোট্ট শিশুও এখন দেশের অবস্থা সম্পর্কে বেশ অবগত। আপনি নাটক সাজিয়ে এতদিন পর গর্ত থেকে বাহির হলেন? মানুষ আপনার মত পাগল না। ওসব আমরা বুঝি।,0,celebrity
স্যার জয়া আহসানের দেবী মুভি দেখেছেন?? যদি দেখেন থাকেন তাহলে আমাদের সাথে রিভিউ শেয়ার করুন।,0,celebrity
কি কমু...,0,celebrity
"যে প্রবৃদ্ধির ধারা চলছে তা দেশের সব নাগরিকের জন্যে সুষম নয়,এটা একটা জায়গায় লম্বালম্বি ভাবে পাহাড়ের চুড়ার মতো উঠে গেছে,সবাই এই প্রবৃদ্ধি র সুফল পাচ্ছে না,২৪ লক্ষ কর্মসংস্থান আরো বিশাল লক্ষ লক্ষ শিক্ষিত বেকার জনগোষ্ঠীর মাঝে তেমন উল্লেখ করার মতো নয়,দেশে সরকারি হিসেব মতে ২৪% লোক দারীদ্রসীমার মাঝে আছে,তাহলে চার থেকে পাচ কোটি লোক দরীদ্র আর লক্ষ  লক্ষ শিক্ষিত / অর্ধ শিক্ষিত নর নারী বেকারদের কর্মসংস্থানে সরকারকে সরাসরি এড্রেস করতে হবে,মধ‍্যম আয়ের দেশের দিকে এগুতে চাইলে।তা নাহলে পুরোনো পুন্জিভূত বেকারদের সাথে আরো লক্ষ  লক্ষ বেকার বেকারের কাতারে সামিল হবে।সেটি সরকারের কাম্য না হলে বাস্তব ভিক্তিক কার্যকর একশান প্লান নিয়ে এগুতে হবে,তবে বর্তমান অর্থনীতি যেভাবে এগুনোর কথা সেভাবে এগুচ্ছে না, বিনিয়োগ স্তবিরতা চলছে,কর্ম সংস্থান হবার ক্ষেত্রে আমাদের যথেষ্ট পরিমান উদ্বিগ্ন হবার কারণ রয়েছে।",0,celebrity
"আমাদের সবারই নিশ্চয়ই মনে আছে এই দেশে মুক্তিযুদ্ধের সন্তানদের কোটা বিরোধী বিশাল একটা আন্দোলন গড়ে উঠেছিল। এই আন্দোলনের এক পর্যায়ে তারা রাজাকারদের পুনর্বাসনে লেগে গিয়েছিল, বুকে ‘আমি রাজাকার’ লিখে দাঁড়িয়ে থাকা একটি ছবির কথা আমি কখনো ভুলতে পারি না।কোটা সংস্কার চাই আন্দোলনকে কোটাবিরোধী বানাই দিলেন।মুক্তিযুদ্ধ হয়েছিলো বৈষম্য দূর করতে,কোটা সংস্কার তো বৈষম্য দূরীকরণের আন্দোলন।এটাই প্রকৃত মুক্তিযুদ্ধের চেতনা।",0,celebrity
রিফাত বিন মুক্তাসিম আহমেদ,0,celebrity
বাড়াটা কেপে উঠলো স্যাড়! শিহরিত 🙊,0,celebrity
জ = তে জাতীয় রাজাকার,0,celebrity
এই স্ট্যাটাস নিয়ে নিয়ে একটা বই লিখেন স্যার।একবারে পড়তে গিয়ে আমি ক্লান্ত।,0,celebrity
"এই দেখি পাশের দেশের গুণকীর্তন! এরা যে আদালতের মাধ্যমে কি ঘৃণ্যসব কাজ কারবার করে, গরুর মাংস খাওয়ার কারণে যেখানে মানুষ হত্যা করা হয় সেই দেশের কোন কিছুই একটি উন্নত দেশের মানুষের জন্য আদর্শ হতে পারে না। আপনি বরং আমেরিকার গল্প শুনান...",0,celebrity
"এডমিন কে ধন্যবাদ, স্যার মারা যাবার পরেও উনার বলা ১ তারিখের পুরানা লেখা পোস্ট করে আমাদের স্মৃতিচারণের সুযোগ করে দেয়ার জন্য 😭😭 Rip",0,celebrity
মাঝে মাঝে সাধারণ জনগণ ও ছাত্রছাত্রীদের কথা শুনতে হয়।,0,celebrity
"খুব করুন ভাবেই লীগের খোয়াড় থেকে আপনাকে পাছায় লাথি মেরে বিদায় করবে হে ঘৃনিত ষ্যাড়, ইতিহাস তাই বলে!",0,celebrity
"আমরা দেশপ্রেমিক। আমরা BSDF. আমাদের পূর্ণরূপ Bangladesh Student Development Foundation.  আমাদের লক্ষ ও উদ্দেশ্য বাংলাদেশের প্রতিটি শিক্ষার্থীকে ""যোগ্যতা সম্পন্ন শিক্ষার্থী"" করে গড়ে তোলা, তাঁদের সুপ্ত প্রতিভাগুলোকে জাগ্রত করতঃ তাঁদের প্রতিভা অনুযায়ী সুনির্দিষ্ট লক্ষের দিকে ধাবিত করা এবং দেশের শিক্ষা বঞ্চিত শিশুদের মাঝে শিক্ষার ব্যবস্থা করা।     ***আমরা অভিনব কায়দায় শিক্ষার্থীদের আত্মবিশ্বাসী, সাহসী ও বিজ্ঞান মনষ্ক  করে গড়ে তুলি,  তাঁদের চিন্তা চেতনার উন্নতি সাধন করি, স্বপ্ন দেখতে শেখাই, স্বপ্ন পূরণে সর্বাত্মক সহায়তা করি।     ***আমরা সুখে দুখে সবসময় শিক্ষার্থীদের পাশে  দাড়াই, তাঁদের সব ধরণের সমস্যার সমাধানে আন্তরিক প্রচেষ্টা করি।      ***জ্ঞান আমাদের শক্তি। আমরা জ্ঞানের আলোয় আলোকিত হই, আলোকিত করি।      ***বায়ান্নোর আন্দোলন, একাত্তরের মুক্তিযুদ্ধ আমাদের চেতনা। অতীত বর্তমানের সকল মনীষী আমাদের আদর্শ। আমরা তাঁদের আদর্শে আদর্শিত হই, আদর্শিত করি আর হুংকার দিয়ে বলি  ""তুমি চাইলেই সম্ভব! যাও, এগিয়ে যাও.....",0,celebrity
যন্ত্রনার এক একটা মুহুর্ত এক একটা যোজনই অনুভুত হয়। আর সে নাস্তিক আস্তিক কিনা তা আললাহ দেখবে।  ব্যাপার হল সে একজন নামী সাহিত্যিক। তার লেখা মানুষ পড়ে। অনুপ্ররনা পায়। নইলে যতটুকু  সে লিখেছে তা পড়ার মত বিশেষ কিছু নয়।  মানুষ তাকে মারতে চাচ্ছে। আঘাত করেও বসেছে। তার খ্যাতীই তার শত্রু।,0,celebrity
এ সমস্ত লেখালেখি বাদ দিয়ে আপনি সরকারের বেশি করে পা চাটেন. এতে করে আপনার স্বার্থ সিদ্ধ হবে.,0,celebrity
"সাধারণ ছাত্ররা ২/৩""ধরে সারা দেশে মার খাচ্ছে,, এতে আপনার কি বমি বমি ভাব হচ্ছে নাকি???",0,celebrity
"আমার সপ্নটা এই বুঝি পূরন হল, আমি খুব চিন্তিত হয়ে পড়েছিলাম, ড.জাফর সোরের মৃত্যুর কথাটা শুনে, কারণ ওনি এতদিন আমাদের কূকর্মের দিকে এগিয়ে নেওয়ার জীবন্ত কিংবদন্তী চিলেন, ওনার মৃত্যু যে আমাদেরকে কতটা হতশা আর বৈশম্য করে পেলেছে তা বলে শেষ করতে পাড়বো না,কারণ ওনার সহচর ও ঘনিষ্ট সহপাটী গন  করুন অবস্তাই এখনো অঙ্গান হয়ে হাসপাতালে শুয়ে আছে, আমি এখনো চিন্তিত তাদের কবে ঙ্গ্যান পিরবে। এই মূহুর্তে আমাদের দেশের যে অবস্তা, আমরা জাফর স্যার মত একজন অভিবাবকের কোন বিকল্প নাই বলে, আমরা যেন এক অন্ধকার যোগে চলে যাচ্ছি, কিন্তু আমাদের জাফর স্যার তা সহ্র করতে পাড়ে নাই, তাই স্যার উপাড় তেকে আমাদের জন্য করুণার বাণী পৌছে দিলেন। সোরের জন্য আমরা জাতি ধন্য হয়েছি তাই স্যারের জন্য শুভ কামনা উপাড়ে ভাল তাকুক। স্যারের উপাড় তেকে যে বাণী পেরণ করেছেন তা পেয়ে আমরা নিজেকে ভাগ্যবান মনে করতে পাড়ি।",0,celebrity
স্যার কয়টা বাজে ভোট দিতে গেছিলেন?? আপনির কার ভোট দিয়ে এসেছেন?? গোপন কক্ষে গিয়ে সিল মারছেন নাকি মাস্তানি করে প্রকাশ্যেই সিল মারছেন??,0,celebrity
আপনার কমেন্ট দেখতে আসি শিবির দেখার জন্য,0,celebrity
"স্যার, অনেকদিন পর আপনার একটা লেখা পড়লাম, যেখানে মুক্তিযুদ্ধ নেই। আপনার সাহিত্যে রুহুল আমিনকে জায়গা দিয়েন প্লিজ। রাজাকারের গল্প পড়তে-পড়তে রাজাকার ভালো লাগা শুরু হয়েছে।",0,celebrity
ধন্যবাদ স্যার আপনার কথাগুলো মনে রাখব,0,celebrity
"আমার প্রিয় শিক্ষক , প্রথমেই ক্ষমা করে দিবেন কারন আজ আমি আপনার চিন্তা চেতনার বিপক্ষে কিছু যুক্তি তুলে ধরবো । প্রথমত আপনি বলেছেন খালেদা জিয়ার আন্দলন মানুষ পোরানোর আন্দলন । তাহলে ২০০৪ সালে হোটেল শেরাটন এর সামনে ১২ জন নিরীহ বাস যাত্রীকে গান পাউদার দিয়ে পুড়িয়ে মারা হয়েছিল । ঐদিন আওমিলিগ এর হরতাল ছিল । ২০০৭ সালে আর্মি দারা  জাহাঙ্গীর কবির নানক কে এরেস্ট করা হয়েছিল  । তিনি বলেছিলেন নাশকতার হুকুম দিয়েছিলেন শেখ সেলিম । ইয়উ টিউব এ চেক করলে পেয়ে যাবেন নানক এর জবানবন্দি । তাহলে আপনার ভাষ্যমতে ঐদিন ডাইনি হাসিনার আন্দোলন কি গণতন্ত্রের জন্য হয়েছিল ? আপনি শিক্ষক , আপনি থাকবেন নিরপেক্ষ ,  সৎ্‌ । আমরা আপনার কাছ থেকে অন্যায় কে অন্যায় বলা শিখবো আর ন্যায় কে ন্যায়  বলব । আমি মোটেই মানুষ মারার আন্দলন সমর্থন করিনা । এই জন্য বাংলার মানুষ হাসিনা , খালেদা কে কখনও ক্ষমা করবেনা । আপনি যখন একটা বিড়াল কে ঘরের মধ্যে বন্দী করে মারার চেষ্টা করবেন তখন একটা সময় বিড়াল আপনাকে আক্রমন করবে । এই ডাইনী  হাসিনা বিরোধী দল কে হত্যা , গুম করে একাকার করে দিয়েছে । পুলিশ কে হাসিনা বানিয়েছে রাষ্ট্রের পোষা  কুকুর । ৫ ই জানুয়ারী একটা হাস্যকর নির্বাচন দিয়ে ক্ষমতাকে এক কেন্দ্রিক করে ফেলেছে । এরশাদ কে  জোর করে নির্বাচন করিয়েছে । আপনি কি নির্বাচন এর নাটক দেখেন নি ? বি এন পি নির্বাচনের পরে টানা একবছর সরকার কে সময় দিয়েছিল । সরকার কেন এখনও ভোটে বিহীন ভাবে তার ক্ষমতা অবৈধ ভাবে ধরে রেখেছে ? আমি নিজে ২০০৮ সালে আওয়ামী কুকুর দের ভোট দিয়েছিলাম । মন্ত্রী এম্পি দের অবৈধ  সম্পদের পাহার দেখার জন্য ? আমি আওয়ামী লীগ কে ভোট  করেছিলাম বিচার বিভাগ , নির্বাহী বিভাগ কে সরকারের পোষা কুকুর বানানোর জন্য ? আপনি জানেন বি এন পি , জামাত , আওয়ামী লিগ সবই খারাপ । কারোর পক্ষে উকালতি করা আপনাকে মানায়না । বাবার কাছ থেকে শিখেছি ----সত্য বলায়ে যদি শত্রুর উপকার হয় তবে তাই কর । অপরদিকে মিথ্যা বলাএ যদি পরিবারের উপকার হয় তবে তা থেকে বিরত থাক । আশা করি আমার বাবার কথাটা মনে রেখে সামনে অগ্রসর হবেন । কষ্ট দিয়েথাকলে মাফ করে দিবেন স্যার ।",0,celebrity
"সুস্থতা চাই, চাই",0,celebrity
মদ খা মদ না খাইলে তোর বুদ্দি হবে না,0,celebrity
প্লিগ খেও স্যারকে গালাগালি করবেননা😭😭😭😭😭😭😂 স্যার আসেন জুমার নামাজ পড়ি😉,0,celebrity
"দ্বায় সারার জন্য কৃতজ্ঞতা।  আপনি আবার ঘুমায়ে যান, দেশ নির্মানে আমাদের পোলপানই যথেষ্ট।",0,celebrity
স্যার আপনি এতো দিন পর কোথা হতে এসেছেন।আমার ভাইরা আপনার গায়াবা জানাজা পড়েছে।আপনি এ পোস্ট না দিলেও পারতেন।কি দরকার মৃত্যু হওয়া বিবেক কে জাগ্রতা করার তাও লোক দেখানো।,0,celebrity
"#muhammad_zafor_iqbal আপনার লেখা পড়ে যে কমেন্ট মাথায় ঘুরছে,, সেটা যদি আপনার বিবেক বরাবর স্যুট করি আপনার মস্তিষ্কের অথর্ব,দূষিত ভাইরাস গুলি বেরিয়ে যাবে।  নবাব সিরাজউদ দৌলার সাথে সাথে গাদ্দারী কে করে ছিলো? মির জাফর.!! আজ মিরজাফর ইতিহাস কলংকিত একটি নাম।  আপনি ইতিহাস নন আপনি বাস্তব মিরজাফর। চাটুকারিতার পূজি নিয়ে সংখ্যালুঘুদের মাথায় গোলামী সূলভ তৈল মর্দন করে, আপনার মিরজাফরী ফেরি করেন। আপনার লেখা পড়ে ঘৃণা আসে। হরহর করে বমি আসে।  আপনি ৭১ রে গর্তে লুকিয়ে থাকা চুন্নি বিড়াল হয়ে জিয়াউর রহমানের মত বাঘের বাচ্চার উপর কলম ধরেন,..!?  চাটুকারিতারও একটা সীমাবদ্ধতা থাকা চাই। ৭১ নিয়ে যেভাবে ঢুলবাজান, মায়া দেখান,দেশপ্রেম যখন ওভারলোড হয়ে, বমি রুপ ধরে হরহর করে নেমে আসে কলমের কালি হয়ে, তখন আপনাকে জিজ্ঞাস করতে ইচ্ছে করে,৭১ নিয়ে মগজ পচা দালালী আর কতদিন করবেন.?",0,celebrity
"লজ্জিত,  হতাশ, ক্ষুব্দ। আপনাদের সুশিল উর্দি      অনেক আগেই খুলে পড়েছে স্যার।",0,celebrity
ঘুম ভাঙছে ওনার 😜😂,0,celebrity
"কেউ যদি চুরি না করেও চোর উপাধি পায়, আর শেষে বাধ্য হয়ে বলে হ্যা আমি চোর।তাহলেই কি সে চোর হয়ে গেল? কোন দৃষ্টিকোন থেকে নিজেকে চোর বললো সেটা যদি বোঝার ক্ষমতা না থাকে তাহলে আরো একটি সায়েন্স ফিকশন লিখায় মনোযোগ দিন,এটাই কল্যাণকর।",0,celebrity
"কোটা বিরোধী আন্দোলন,ছাত্রদের নিরাপদ সড়কের আন্দোলন,গরীব লোকের হাহাকার-এসব কিছুতেই আপনি চুপ ছিলেন।ভেবেছিলাম আপনি হয়ত দেশের সব ব্যাপারে কথা বলতে চান না,কিন্তু আপনি যে কেবলমাত্র তেলবাজি করতে চান তা আমার ধারণায় ছিল না।যদি ধারণায় থাকতো তবে আপনার উপর যখন হামলা হয়েছিল তখন আর এত কষ্ট পেতাম না।লজ্জা করে না নিজেকে মানুষ ভাবতে?",0,celebrity
আপনার ধারনা ভুল।,0,celebrity
নু নু ভুন্ডু এটা মেনে নিতে পারলুম না..🙈 . মারা খেয়ে (থুক্কু) মরে গিয়ে এখন ভং ধরছো. 😑😓☝,0,celebrity
মাহমুদ হাসান Mahbub Habib SheNiz Sultana Arif Ul Islam,0,celebrity
গর্তের মুক্তিযোদ্ধা 😆,0,celebrity
"ধৈর্য ধরেন,কেউ ঠেলাঠেলি করবেন না প্লিগ.. সবাই কমেন্ট করার সুযোগ পাবেন...😂😂😂",0,celebrity
"""আইন নিজের হাতে তুলে নিবেন না"" এই কথা টা বলতে আসছেন তাই তো?",0,celebrity
"নাহ, স্যার এবারো চাটুকারিতা গন্ধটা গেলোনা। চেষ্টা করেছিলেন। কিন্তু চাটুকারিতা আপনার রন্ধে রন্ধে,, শিরা উপশিরায়।",0,celebrity
"""আমি রাজাকার"" --- এই ট্যাগটিতে আর কেউ খুশী হোক বা না হোক জামাত শিবির ধর্মব্যাবসায়ীরা খুশীই হয়েছে।",0,celebrity
দেওয়ালে পিঠ ঠেকে গেছে অথচ প্র্যাকটিকাল খাতা এখনো আঁকা এবং লেখা হয়নি।পরীক্ষার আর বেশিদিন বাকি নেই।পড়াশোনা এবং প্র্যাকটিকাল খাতা আঁকা ও লেখা নিয়ে হিমশিম খাচ্ছেন? কোন সমস্যা নাই।আমরা আছি কিজন্য?যোগাযোগ করুন-01791643953 এই নাম্বারে।  [বি.দ্র-আমরা এখনো হাত অত লম্বা করতে পারিনি বিধায় চট্টগ্রামের বাইরে কাজ করতে পারছি না।অতএব শুধুমাত্র চট্টগ্রামের শিক্ষার্থীদের জন্য করতে পারছি।তবে কেউ যদি কুরিয়ার খরচ দিয়ে করাতে চান সেক্ষেত্রে দেশের যে-কোন প্রান্তের কাজ করে দিতে পারব।],0,celebrity
"""একজন মানুষ তার স্বপ্নের মত বড়""",0,celebrity
প্রথম ৫ টাই ছিল একটা নিদৃষ্ট দলের প্রতি টান। এর ভিতর ১/২ টা থাকলে আমি উনার সাথে একমত হতে পারতাম। বা তিনি কথা গুলো নির্দলিয় ভাবে বলতে পারতেন।,0,celebrity
"বর্তমান পরিস্থিতিতে আমরা আপনার কাছ থেকে কোন লেখা পাবো, এমনটা আশা করিনি স্যার। এই লেখাটি লেখার চেয়ে কিছু না লেখাই ভাল ছিল। যাহোক, আমরা চাই- সবাই ভাল থাকুক, আমরা যত কষ্টেই থাকি না কেন। আমাদের বুঝতে অসুবিধা হচ্ছে না যে, আপনি একটু বেশিই ভাল আছেন এবং থাকবেন। কারণ আপনি ডাবল ফুলের মত পবিত্র যা আপনার লেখায় অতি সুন্দরভাবে ফুটিয়ে তুলেছেন। ভাল থাকুন স্যার।",0,celebrity
সবগুলো কমেন্ট একসাথে করে একটি বই বের করা উচিত। তাহলে আগামী বছরের একুশের বই মেলায় বেস্টসেলারের মর্যাদা পাবে। অন্যপ্রকাশ ভেবে দেখতে পারে।,0,celebrity
"""লেখাপড়া করে যে, অনাহারে মরে সে; জানার কোনো শেষ নাই, জানার চেষ্টা বৃথা তাই""। আমরা হিরক রাজার দেশে আছি।",0,celebrity
"আপনার এতো আগের লেখাতে মন্তব্য দেয়া অর্থহীন কাজ। তবু, সরকারের এমন দমন পীড়ন নিয়ে কিছু বলতে মন চাইছে। যেকোন বুদ্ধিমান সরকার তার কর্মকান্ডের সমালোচনা থেকে নিজের কাজের বিষয়ে সতর্ক হয় ও শিক্ষাগ্রহণ করে থাকে। এমন নিপীড়ন করে মুখ বন্ধ করতে চায় না। সরকারের বুঝা উচিৎ ছিলো, মুখতো একটি দুটি নয়। হাজার হাজার মুখ বন্ধ করতে গেলে নিজের দেশের সব মানুষই হয়ত এই কাতারে দাঁড়িয়ে যাবে। এই বিষয়ে সরকারকে আরো সচেতন হতে হবে।",0,celebrity
"তেল বাজ শিক্ষক সোনার ছেলেদের নিয়ে কি বলবেন, যারা ৪ সন্তানের জননী কে ধর্ষণ করেছে",0,celebrity
সবি বুঝি!কিন্তু কিচ্ছু কমু না!,0,celebrity
স্যার কবর থাইকা আইছেন! এই শালার পুতেরা মুনাজাত ধর?,0,celebrity
একটি দুঃখের গল্প,0,celebrity
আপনার তো সমস্যা থাকার কথানা আওমিলীগ ক্ষমকায় আসাতে আপনারই লাভ বেশি চাটুকারিতা করে আরো ৫ টা বছর কাটিয়ে দিতে পারবেন,0,celebrity
"আমাদের যশোর বোর্ডে ২০১১ সালে ইংরেজি প্রশ্ন খুব   কঠিন হয়েছিল,প্রতেক বার যশোর বোর্ডে প্রশ্ন খুব কঠিন হয় ,পাশের হার কম  থাকে,A++ এর সংখ্যাও কম থাকে  তার  পরও আমরা   A++  পেয়েছিলাম",0,celebrity
আম্লীগের কাছ থেকে এতো ম্রা খেয়েও তাদের দালালি করেন... লজ্জা নাই আপনার... দেশের বিশিষ্ট ভীতু বুদ্ধিজীবী.. যিনি যুদ্ধে গর্তে লুকিয়ে ছিলেন।,0,celebrity
দোয়া করি যাতে খুব দ্রুত সুস্থ হয়ে উঠুন।,0,celebrity
স্যার আগে বলেন ' নিজের মনের ভাষা লিখে যদি কমেন্ট করি' আইমান সাদিকের মত ডিলেট করে দিবেন না তো?,0,celebrity
একই দিনে দুটি বিনোদন হজম করতে পারছি না। 1> আপনার ও ইচ্ছে জাগলো মানুষ কমেন্ট পরিবর্তন করে ভালো কমেন্ট করে কিনা। 2> আরে মিয়া কমেন্ট পড়েন কেন !  আমার চাকুরী খাওয়ার বুদ্ধি করছেন..!,0,celebrity
"আপনার লেখা দেখলেই হড় হড় করে বমি আসে।আপনার বইগুলো এমন জায়গায় রাখছি যেন, আপনার চেহারা দেখতে না হয়।",0,celebrity
"হ্লা,মুক্তিযুদ্ধের ফেরিওয়ালা, কয়দিন আগেনা আপনার গায়েবানা জানাযা হলো 😛",0,celebrity
"ভালো থাকেন, থাকবেন সবসময় এই দোয়া করি।আপনার মতো বিশাল মন না আমার।আমাদের আগামি প্রজন্ম আপনার দিকে তাকিয়ে, আপনাকে আর অনেক বছর বাঁচতে হবে",0,celebrity
আমি গণিতে পড়ি। নন মেজর হিসেব ফিজিক্স পড়ছি। ৯-১০ থেকেই আমার ফিজিক্সে ঘাটতি ছিল। শিক্ষার কোন বয়স নাই তাই বইটি আমার অনেক উপকারে আসবে।     আর বইটি বাজারে আসলে সবাইকে পড়তে বলব।,0,celebrity
"স্যার আপনার জীবনের সেইদিন টার কথা একবার ভালো করে শোনান না? ওই যে,  যেইদিন কোদাল দিয়ে গর্ত খুড়ে খুড়ে আপনি প্রায় যুদ্ধ টা করেই ফেলেছিলেন!!!!!!!",0,celebrity
"ভরা যৌবনে যে যুদ্ধে যায় না, সেই রাজাকার, আর রাজাকারের কোন মতামত জনগন গ্রহন করেনা।",0,celebrity
"অসম্ভব ভালো লিখেছেন স্যার। আচ্ছা স্যার, কয়টা ভোট দিয়েছেন ? স্বাধীনতার স্বপক্ষের হাতকে শক্তিশালী করতে  বেশি বেশি ভোট দিয়েছেন নিশ্চই... ?",0,celebrity
গায়েবি জানাযা শেষ হঠাত উধাউ। এবার একটা ফ দিয়ে যাই। যখন সময় হবে তখন মদ খাব আর কমেন্ট পড়ব✌,0,celebrity
তোকে গালী দিলেও  আমার গালীর অসম্মান হয়,0,celebrity
ট্রেঞ্চ থেকে বের হইছ বাবা? 🐸,0,celebrity
"জিয়ার সামনে ছিল দুর্ভিক্ষের ইতিহাস, রক্তারক্তির ইতিহাস, লুটপাটের ইতিহাস, বাংলাদেশে ভারতের নগ্ন হস্তক্ষেপের ইতিহাস। এগুলোকে মাড়িয়ে জিয়াকে সামনে এগোতে হয়েছে। জিয়া যখন ক্ষমতায় আসেন তখন মানুষের পেটে ভাত ছিল না, কাজের সুযোগ ছিল না, গায়ে জড়ানোর কাপড়েরও অভাব ছিল। জিয়ার জন্য তখন ""চেতনা"" নামক ভাব বিলাসের সময় ছিল না।  ৭১-৮১ টাইমলাইন দেখলে পর্যন্ত পরম শত্রুও স্বীকার করবে জিয়ার মধ্যে ""চেতনার"" আধিক্য না থাকলেও প্রচন্ড ""দেশপ্রেম"" ছিল। জিয়া শুধু সে পথেই এগিয়েছেন। আর মানুষ ক্ষমতা চায় নিজের উদরপূর্তি করার জন্য, জিয়া এই ক্ষমতা তো নিজের আখের গোছানোর জন্য ব্যবহার করেননি, জিয়ার সততা এখনো প্রবাদতুল্য। অনেক ঘাত-প্রতিঘাত-বিপ্লব-প্রতিবিপ্লব পেরিয়ে একটা সমৃদ্ধ বাংলাদেশ গড়ার জন্য মৃত্যুর আগ পর্যন্ত কাজ করে গেছেন!  এবার আসা যাক ""পাকিস্তানপন্থী"" শব্দটার ডিসেকশনে। এই শব্দটা শুনলেই এখনকার চেতনাপন্থী জেনারেশন নাক কুচকে ফেলে। ১৯৭১ সালে অখন্ড পাকিস্তান চাওয়া লোকদেরই বলা হয় পাকিস্তানী। আমরা স্বাধীন বাংলাদেশের পক্ষে অবস্থান নিয়েছিলাম, কিন্তু কেন তারা অখন্ড পাকিস্তানের পক্ষে ছিল সেইটা কখনো ভাবনায় এনেছি? সেইটা নিয়ে বড় থ্রেডে কখনো আলোচনা করা যাবে। যারা পাকিস্তানপন্থী ছিল, তাদের মাথায় কি শুধুই গোবর ছিল?  শুধুমাত্র পাকিস্তানের পক্ষে মত দেয়ার জন্যই কি তাদের সব বর্জনীয়? (আই রিপিট নো স্পেইস ফর মানবতাবিরোধী অপরাধী,শুধুমাত্র তাদের কথা যারা অখন্ড পাকিস্তান চেয়েছিলেন) বিভিন্ন সুত্র কিন্তু এইটা বলছে না। নীলিমা ইব্রাহিমসহ বিভিন্ন সুত্র যেসব নাম আমাদের জানতে পারি প্রত্যেকটাই পিলে চমকানোর মতন ভয়াবহ! ফররুখ আহমেদ, মুনীর চৌধুরী, আহসান হাবিব, ফতেহ লোহানী,এ টি এম শামসুজ্জামানসহ অনেক প্রথিতযশা লোকই এই তালিকায় ছিলেন।  জিয়ার সরকারে আর শাসনক্ষমতায় মুক্তিযোদ্ধার পাশাপাশি হরেকরকম মানুষ ছিল। এখানে পাকিস্তানপন্থী শাহ আজিজুর রহমানেরাও ছিল। জিয়া চেয়েছিলেন তাদের মেধাগুলো দেশের জন্য কাজে লাগাতে এবং একই সাথে এদের মেধা যেন বাংলাদেশের বিরুদ্ধে কাজে না লাগে সেটার রাস্তা বন্ধ করতে। আরেকটা ব্যাপার হচ্ছে,জিয়াউর রহমানের সরকারে উল্লেখযোগ্যসংখ্যক মুক্তিযোদ্ধা থাকলেও রাষ্ট্রযন্ত্রের বিভিন্ন জায়গায় ""সক্ষম"",""যোগ্য"" এবং ""দূরদৃষ্টিসম্পর্ক"" লোকের অভাব ছিল, যেটা কাটাতে তিনি এই লোকদের এখানে শরীক করেন। কিন্তু অবশ্যই এখানে একটা বড় ব্যাপার ছিল তারা ""বর্তমান"" বাংলাদেশের প্রতি লয়াল ছিল কিনা। তারা তার প্রমাণ দিয়েছেন।",0,celebrity
"দেশের সবচেয়ে বড় ঘটনায় আপনি অংশগ্রহণ করেন নি কেন? দেশকে ভালোবাসে না? নাকি দালাল প্রজাতির সুবিধাভোগী মানুষ আপনি যে দেশের সবচেয়ে বড় ঘটনার সময় আপনি কোন ভূমিকাই নিলেন না। ভং ধরে বসে রইলেন। সুযোগমত বাতাস যেদিকে বয় সেদিকে পাল তুলে দেয়ার জন্যে? এখন ৪৭ বছর পরে আপনার মনে হচ্ছে সেটা দেশের সবচেয়ে বড় ঘটনা ছিল, বাহ! তাইলে আমিও এখন আপনেরে গালাগালি করবো, তুমুল গালাগালি করবো, চরম লেভেলের গালাগালি করবো। এরপর ২০ বছর পর প্রবন্ধ লিখবো আপনি আসলে ভালো মানুষ ছিলেন, গালাগালি করা ঠিক হয় নাই। অকে?  চেতনাবাজির ব্যবসাটা প্লিজ বন্ধ করেন। মানুষ যথেষ্ট জানে আর বুঝে। আপনের ফাঁকা বুলিতে আর কাজ হয় না জনাব।  আওয়ামীলীগ, বিএনপি আর জামায়াত এর তাও একটা নির্দিষ্ট পরিচয় আছে। তাদের একটাই রূপ। আপনে আগে নিজের রূপ ঠিক করেন। বহুরূপীপনা বাদ দেন। বৃদ্ধ হয়ে গেছেন এখন একটু মানুষ হোন।",0,celebrity
"ঘটনা ঘটালো আওয়ামী লীগ আর আপনি লিখলেন বিএনপি-জামাতের সময় এমন অনেক হইছে, সব কিছুতেই ত্যানা না প্যাঁচালে হয় না?আরও লিখলেন এরকম শুধু একটি ঘটনা ঘটেছে, কেন কয়টি ঘটলে আপনি আরাম পাবেন? এমন অনেক ঘটনাই ঘটে কিন্তু আপনাদের মতো চেতনাবাজ দের জন্য চোখে পরে না। সাধারণ মানুষ যখন সামনে নিয়ে আসে তখন আপনাদের চেতনার দন্ড দাঁড়িয়ে যায়। লজ্জা করে না আপনার?",0,celebrity
100%right! তবে আপনার নিরপেক্ষতা অবলম্বন করা উচিত।,0,celebrity
পোস্টটি পড়ে আচমকা আমার হাগা আটকাইয়া গেছে💩💩💩,0,celebrity
"একটা ব্যাপার চোখে পড়ল । দশম অধ্যায়ে ২১৮ নং পৃষ্ঠায় "" পৃথিবীতে ১০৯ টা পরমানু আছে "" লেখা । এটা সম্ভবত "" ১০৯ ধরনের পরমাণু আছে "" হবে । আর আমার জানামতে এটা বর্তমানে ১১১ । :)",0,celebrity
"দুষ্ট ছেলে!! তুমি ঘুমায় থাকো, বেহুশ হয়ে ঘুমিয়ে থাকো। কেমন??",0,celebrity
"জ্ঞান আহরণের জন্য পোস্ট পড়বো, নাকি কমেন্ট পড়বো ; আমি দ্বিধায় পড়ে গেলাম",0,celebrity
"দোয়া করি, আপনার মৃত্যু যেন বিএনপির শাসনামলে হয়।",0,celebrity
আহা আমরা আপনি মরে গেসেন ভেবে কুলখানির খাওয়ার জন্য প্রিপারেশন নিচ্ছিলাম,0,celebrity
এই ভন্ডের গুণকীর্তন করাকে অনেজকে জ্ঞানীর ভাবসাব মনে করে 😁 তাই এই আবালেরা মিডিয়া র বানোনো হিরু ইকবাললের  লুচ্চামি দেখেনা।।,0,celebrity
wow.nic,0,celebrity
"স্যার! দেখলেন, ভাল ইস্যুগুলোর সমালোচনা করতে গেলে নিজেকেই সমালোচিত হতে হয়...",0,celebrity
"দেশের প্রতি ভালোবাসা আমাদের ঠিকই আছে।ipl এর খেলা দেখি শুধু সাকিবের জন্যে,কারণ ওর নামের সাথে যে বাংলাদেশে নামটাও চলে আসে।এটা জাস্ট একটা উদাহরণ। বরং এদেশের কিছু স্বার্থপর   মানুষেরা নিজের স্বার্থ অর্জনের জন্যে অতিরিক্ত চেতনা দেখিয়ে আমাদের দেশপ্রেমটা নষ্ট করতেছেন!!!",0,celebrity
ওয়াক থু ।,0,celebrity
"thanks Sir.....i miss you...এভাবে আপনি লেখতে থাকেন Sir.....তহলে আমরা কিছু জানতে পারবো.,....::::::::::::::::://////////:::::::::::::PST::::::::",0,celebrity
"আশা করেছিলাম আপনি আমাদের ছোটো ভাই-বোনদের সাথে পথে থাকবেন। এটুকু দায়িত্ববোধ আপনার কাছ থেকে আমরা আশা করতেই পারি। অথচ এই দায়সারা লেখা লিখে আপনি যেন আমাদের উদ্ধার করলেন, দয়া করলেন!!!",0,celebrity
ইন্নালিল্লাহি ওয়া ইন্নালিল্লাহি রাজেউন 😭😭,0,celebrity
দালাল,0,celebrity
"আপনি  যা বললেন বা বলবেন, তাই সঠিক হলে বা হবে বলে ধরে আপনাকেই বাংলাদেশের মানুষ নেতা বানায় দিতো... আপনি আলোচনা করে নতুন নির্বাচনের মাধ্যমে সত্যিকারের গনতন্ত্র শুরুর কথা কোনো বলেন না? ??? বিএনপি জামাত অন্যায় করছে কিন্তু একতরফা কথা বলে আপনি  আমাদের এ প্রজন্মকে নিষ্ঠুর আঘাত করলেন...",0,celebrity
গুজবে কান দিয়ে পাশে থাকুন সব্বাই!😂,0,celebrity
সব কমেন্ট পরে মাথা হ্যাং হয়ে গেছে😂,0,celebrity
কেউ বমি না করে যাবেন না!,0,celebrity
গুড,0,celebrity
সবাই লাইনে দাঁড়ান কেউ ঠেলাঠেলি করবেন না সবাইকে হড়বড় করে বমি করার সুযোগ দেওয়া হবেl,0,celebrity
কমেন্ট পড়তে আসছি ☺,0,celebrity
আহো ভাতিজা আহো তুমার লাইজ্ঞা বকরি ডা রেডি কইরা রাখছি আর অইটা তুমার পাছা দিয়া হান্দাই দিয়াম😂,0,celebrity
মদ খাব। আপনার গায়েবানা জানাজা পরে ফেলেছি।,0,celebrity
অনেক শুভেচ্ছা স্যার :),0,celebrity
"ধন্যবাদ স্যার, একটু দেরিতে হলেও আপনার শুভ বুদ্ধির উদয় হয়েছে দেখে খুশি হলাম। যদিও আপনি যে একজন সুবিধাবাদী, আপনার লেখাতে তা স্পষ্টভাবে প্রকাশ পেয়েছে। আপনি না দেখে কোন কিছু না পড়ে কি ভাবে এই লেখা লেখতে পারলেন এটা জাতির কাছে খুবিই হাস্যকর মনে হচ্ছে। আবার আপনি আপনার লেখাতে সরকারের সমালোচনা করেছেন, আপনার মত পা চাটা গোলামের মুখে সরকারের সমালোচনা  মানায় না। স্যার কিছু মনে করবেন না।",0,celebrity
আজ বৃহস্পতিবার রাত না হলে ধরে নিতাম লেখাটা পুরাই গুজব বা গজব যাই হোক।আমরা সত্যিই বিচলিত,0,celebrity
এইরকম একটা ফালতু লেখা পড়ে সময় নষ্ট করলাম😡😡,0,celebrity
আপনি একজন বুদ্ধি প্রতিবন্ধী,0,celebrity
স্যার আপনি আমার খুবই পছন্দের একজন মানুষ। আপনার লেখা আমার খুবই প্রিয়। আজই প্রথম সুযোগ হলো জানাবার তবে কোনদিন সানিধ্য পাবো কিনা জানিনা!!! চারুকলা নিয়ে আমি পড়াশুনা করিনি তবে ভালবেসে এঁকে চলেছি আপনাদের আশির্বাদে আজ চর্চা চালিয়ে যাচ্ছি। ২০০৭ এ করা আপনার  প্রতিকৃতিটি কি কোনদিন আপনার কাছে পৌছাতে পারবো । নাকি স্বপ্নই থেকে  যাবে এ ক্ষুদে আঁকিয়ের । আমার বাড়ি যশোর জেলার অভয়নগর থানার নওয়াপাড়াতে। আমার নম্বর 01728932293।,0,celebrity
মাঝে মাঝে স্যার আপনাকে যখন খুব মনে পরে তখন আপনার এই শেষ লেখাটি পড়ি। আজ আপনি বেচে থাকলে হয়তো বাচ্চাগুলো একজন অভিভাবক পাশে পেত। ওপাড়ে ভালো থাকবেন স্যার,0,celebrity
ধন্যবাদ স্যার। অনেক কিছুই জানতে পেরেছি আপনার লেখা থেকে,0,celebrity
"স্যার যদি এই বছরে সমন্বিত ভর্তি পরিক্ষা নেওয়া হয়,তাহলে আমাদের 2nd টাইমারদের কি হবে?আমরা কি পরিক্ষা দিতে পারবো।।প্লিজ উত্তরটি দিলে ভালো হতো।।।স্যার",0,celebrity
স্যার একটা সাক্ষাতকারে বলসিলেন স্যার এফবি চালান না..বুঝেন ও না..  তো এই পেইজ টা চালাই কে??  স্যার সেজে আমাদেরকে কেউ ভুল বুঝাচ্ছে না তো??  স্যার তো এরকম কিছু বলতে পারেন না..আমি কিছুতেই বিশ্বাস করি না এগুলা স্যারের কথা!!!,0,celebrity
আপনার লিখায় এখন হডহড করে বোমি করতে মন চায়,0,celebrity
স্যার ভয় নেই!  কুত্তারা গেউ গেউ করবেই!,0,celebrity
শুভ কামনা স্যারের জন্য,0,celebrity
চেতনার খনি😉 আমার চেতনার ট্যাঙ্কি খালি হয়ে গেলে উনার লেখা পইড়া পুনরায় লোড করে নেই😜,0,celebrity
খোদা আপনার কথা শুনেছেন স্যার!,0,celebrity
"বুদ্বিজীবী শব্দটাকেই একটা গালি বানিয়ে ফেলেছে এই সুবিধাবাদী, উচ্ছিষ্ট ভোগী,  মেরুদণ্ডহীন চাটুকারের দল",0,celebrity
কমেন্ট হপ্পে।,0,celebrity
"এখানে কমেন্ট করতে ইচ্ছে করে না,,কমেন্ট করলেই হ্লার হাহা'র হুরাহুরি লেগে যায়😂😂😂",0,celebrity
"স্যার, আপনার পোস্ট আমি পড়ি না,কমেন্ট পড়তে আসি😂😂",0,celebrity
আমার মতো ক্ষুদ্র মস্তিষ্কের একটা ছেলে প্রতিনিয়তই উন্য়নমূলক চিন্তা করে যাচ্ছে । আর তার অধিকাংশ চিন্তা গুলিকে বাঁচিয়ে রাখছে  ভবিষ্যতের জন্য । এগুলির কমপক্ষে একটি তো আমি বাস্তবায়ন করবোই করবো ।,0,celebrity
শুভকামনা রইলো।,0,celebrity
www.newspoint.today,0,celebrity
অামাদের এলাকার শিক্ষকরা পশ্ন নিয়ে এসে পরীক্ষার্থীদের স্কুলে বসিয়ে পরিয়ে তারপর পরীক্ষা দিতে পাঠাচ্ছে।সবাই জানছে দেখছে কেউ কিছুই বলছে না।,0,celebrity
"সত্যিকার মুক্তিযুদ্ধের চেতনার প্রতিফলন দরকার। এ বাক্যটা না বুঝে নিশ্চই মন্তব্য করেছেন। আজ মুক্তিযুদ্ধের স্লোগানে ব্যবসা হচ্ছে। ভূয়া মুক্তিযোদ্ধায় ভরে গেছে দেশ। এই মূহুর্তে কি সঠিক চেতনা বিকাশ জরুরী না। যদি তা না করা হয় তাহলে তো জাতির শ্রেষ্ট সন্তানদের নিয়ে তুচ্ছ তাচ্ছিল্য করা হবে। আমার বোধগম্য নয় কেন আপনি এটা বুঝতে ব্যর্থ।  আর হ্যা, এক্যফ্রন্ট যদি কোটা আন্দোলন কারীদের (আপনি বলেছেন কোটা বিরোধী) ইশতেহারে অনুসরণ করেই তাকে তবে তারা বাংলাদেশের উজ্জল ভবিষ্যত কামনা করছে। কারণ এ তারুণ্যই বিনির্মাণ করে আগামীর বাংলাদেশ।   জাফর ইকবাল সাহেব আজ যে তরুণদের বিরুদ্ধে কলম ধরেছেন, সেই তরুণই আপনার উপর হামলার সময় সারা দেশ কাঁপিয়ে তুলেছিল।  অবশ্য আপনার মতো একজন দলান্ধ, এজেন্ট এর কাছে এর থেকে বেশি কিছু আশা করা বোকামী!",0,celebrity
আপনাকে বাংলার মানুষ কেমন চোখে দেখে এই কমেন্টগুলো তার প্রমান।আপনার মতো মানুষের কাছ থেকে কিইবা আশা করা যাই,0,celebrity
ভারতবর্ষের জাতীয় সঙ্গীত বাংলা ভাষায়! ওয়াও! 🔫,0,celebrity
কোটা সংস্কার চাই,0,celebrity
শুভ সকাল স্যার,0,celebrity
আমিও পাকিদের কোন জিনিস কিনিনা। স্যারের ব্যাপারটা আগেই জেনেছি স্যারের বিভিন্ন লেখা থেকে।,0,celebrity
"ওহে ধারী শয়তান, তোর শয়তানি সবাই বুঝে এখন।",0,celebrity
আমি তো এই খবর শুনেই অবাক...??,0,celebrity
আপনি সঠিক স্যার,0,celebrity
"স্যার আমি আপনার সাথে এক মত আমি ভালবাসি আমার নিজেকে আর আমি সার্পোট করি আমার দেশকে আর আনন্দ পাই খেলা দেখে।এটা বাংলাদেশের  জন্য বাঙ্গালি জাতির জন্য একটা অপমান জনক বিষয়। এখন আমরা খেলা দেখে বিনোদন করি না বিনোদন করি হলো আমার অপজিট র্টিমের সার্পোটার ভেঙ্গে করে আনন্দ পাই তাদেরকে ট্রল করে ,হেও করে।আমরা ভাল জিনিসটারে ভাল ভাবে খাইতে ভালবাসি না।",0,celebrity
"আমি ক্ষমা প্রার্থী,  গর্ত জাফরের মত চামচার পোস্টে কমেন্ট করার জন্য, গুরুত্বপূর্ন মাদারচোদ হিসেবে তার নিজেকে প্রকাশ করার চেষ্টা করার বিরোধিতা করার জন্য।",0,celebrity
বেরশিক ফলোয়ারগন!  কমেন্ট গুলো জাতির জন্য হাইস্যকর!  এইটা জাতির জন্য হাইস্যকর 😝😜,0,celebrity
ষাঁড় আপনার চোখে মনে হয় কুত্তায় মুতি দিছে।?? আপনার মতো বদমাশ গুলো যতদিন বেঁচে থাকবে ততদিন এই দেশ গ্লানি মুক্ত হবে না কুত্তার বাচ্চা,0,celebrity
"যুক্তির সারল্য আমায় মুগ্ধ করেছে- ""বঙ্গবন্ধু ও বাংলাদেশ সমার্থক।তাই যারা বঙ্গবন্ধুকে অস্বীকার করে তারা বাংলাদেশকেই অস্বীকার করে।এদেশের মাটিতে থেকে এদেশকে যারা অস্বীকার করে তাদের এদেশে থাকার কোনো অধিকার নেই!"" হাহাহাহা   এমন পাম দিলো খোদ হাসিনা ম্যাডাম পাও লম্বা মাথা গোল [পাগল] হয়ে যাবে।",0,celebrity
"ভাবতেই লজ্জা লাগে যে এইরকম একটা হিজড়ার কাছ থেকে একটা অটোগ্রাফের আশায় ২০০৮ সালের বইমেলায় এক ঘন্টা লাইনে দাঁড়িয়ে ছিলাম। যার সত্য বলার সাহস নাই, তার মুখে বড় কথা বলার ও অধিকার নাই। ধিক! শত ধিক!",0,celebrity
বাংলাদেশের ছাত্রসমাজের কাছে আপনি কোন পর্যায়ে ছিলেন জানেন? আর এখন কোন পর্যায়ে নেমেছেন তা কি বুঝেন?,0,celebrity
য‌তোগু‌লো মানুষ ক‌মেন্টস  ক‌রে‌ছে তার ৯৯% পার‌সেন্ট  ই  ওনার বিপ‌ক্ষে  কথা ব‌লে‌ছে। এ‌তোগু‌লো  মানুষ ভুল বল‌তে পা‌রেনা। সুতরাং ওনার পোস্ট  করা  ছে‌ড়ে দেওয়াই  ভা‌লো। কারন উ‌নি  দে‌শের  কোন  উপকার এ  আস‌তে‌ছে না।  এসব মান‌ু‌ষের প্র‌তি সবার ঘৃণাটাই এখন বে‌শি।,0,celebrity
"যাইহোক । শেষ অবধি মৃত মানুষটি আমাদের মাঝে ফিরে এল। কেউ তারা হূরা করবেন না, লাইনে দাঁড়ান , মৃত ব্যক্তিটি জীবিত হয়ে আমাদের মাঝে ফিরে আসায় , সুন্দর করে গুছিয়ে গাছিয়ে গালি দিয়ে অভিনন্দন জানানোর জন্য  সুযোগ দেওয়া হবে সবাইকে। সবায় বলেন আমীন।",0,celebrity
রাজাকারের বাচ্চারা এখানে কি চায়???,0,celebrity
"Yes sir.u r absolutely right.its da time to do so. Amader noya projonmer supto buddijibider amra hotta korte debo na ..kokkhono na.Bangladesh amar desh, Sabash Bangladesh",0,celebrity
ফালতু লোক আপনি । হুমায়ুন আহমেদের গর্ত থেকে বের করার ইতিহাস শুনেই বুঝতে পেরেছিলাম ।,0,celebrity
মাগার কমেন্টগুলো পড়েই আমার কমেন্ট করার শখ শেষ হয়ে গেছে😃😃,0,celebrity
এরশাদ এর হারিয়ে যাওয়া ভাই👿,0,celebrity
যদি রাজাকারের বাচ্চা না হতো তাহলে গঠনমূলক সমালোচনা করত এখানে গালিগালাজ করতো না হচ্ছে মেধাবীদের নমুনা কমেন্ট বক্সে এসে গালিগালাজ করে,0,celebrity
স্যারকে চেতনাবিষয়ক মন্ত্রী হিসেবে দেখতে চাই।,0,celebrity
চলে স্যার নামাজ পড়ে আসি :-) পুলিশ ডাইকেন না যেনু :D,0,celebrity
বইকেনার টাকা পাইই না সবসসময়।  তাই পিডিএফ পড়ি 😭😭😭,0,celebrity
স্যার আমার খুব প্রিয় একজন ব্যাক্তি এই মাদারচোদ কে আমি ফ্রিজে ঢুকিয়ে রাখতে চাই যাতে করে পঁচা গন্ধ না বের হয়। পেত্নি চো**আ শালারপুত ;),0,celebrity
একটা বিড়ি ধরাইয়া বসে গেলাম কমেন্ট পরতে,0,celebrity
আপনাকে স্যালুট জানাই সির...আপ্নি দীর্ঘজীবী হন।,0,celebrity
ভোট জনগণ দিলো কই ভোট তো রাতেই হয়ে গেলো,0,celebrity
"স্যার,সৃষ্টিকর্তা আপনাকে আমাদের জন্যে অবশ্যই বিপদমুক্ত করে রাখবেন",0,celebrity
গরুর,0,celebrity
"অবশেষে, গর্তে থেকে জাফর সাপ বের হয়েছে :O । এত কলা কৈ পান স্যার? আমরা অলরেডি জেনে গেছি জাফর ইকবাল নামে কোনো স্যার বেঁচে নেই :\ । আপনি বরং কবরে বমি করার ঔষধ খেয়ে চুপচাপ শুয়ে থাকেন :-D ।  আপনার সাধু সাজার চেষ্টা করার পোস্টে আমরা হড়হড় করে বমি করে দিলাম 3:)",0,celebrity
মদ চলছে কমেন্ট পড়ছি,0,celebrity
"বয়সের ভারে নুয়ে পরা এই বিশেষ প্রাণীটিকে নিয়ে আপনাদের এত বাজে কথা পড়তে পড়তে আমি একটা জিনিস বুঝলাম, এই শ্রেণীর মানুষ গুলো মনে করে আমার যারা পাঠক তারা সবাই ভোদায়।অথচ এটা বুঝেনা একটা লেখার প্রতিক্রিয়া যখন এত খারাপ হয় তখন সে নিজে কত খারাপ।",0,celebrity
কমেন্ট পড়তে আইসি,0,celebrity
সুজা প্রশ্ন স্যার আপনিকি ঈমানে মুফাসসাল বিশ্বাস করেন কি না।,0,celebrity
আপনি কোন বালের মাস্টার আমার মাথায় ধরে না।,0,celebrity
"আপনার জন্য আমি উপন্যাস লিখব,, এতোদিন কোথায় ছিলেন?? অংশ ২"" অংশ ১ আয়মান সাডিক এর জন্য লিখেছিলাম তাই আপনাকে দ্বিতীয় অংশে রাখা 🐸🐸🐸🐸🐸",0,celebrity
you r right sir,0,celebrity
চাটারুরা যখন জাতির বিবেক হওয়ার ভং ধরে 👿,0,celebrity
আমার এই মূল্যহীন জীবনের আয়ুটুকু আপনাকে দিলাম স্যার।♥♥,0,celebrity
মহান মালিকের বিচারের কাঠগড়ায় একদিন সবাই দাড়াতে হবে... জ্ঞাণ বিবেক বুদ্ধি কোথায় কাজে লেগেছে সে ব্যাপারে চুলচেরা হিসেব দিতে হবে... হয়তো আজ আমরা দেখতে নাও পেতে পারি কিন্তু ঐ দিনের অপেক্ষায় রইলাম,0,celebrity
পৃথিবী থেকে মানুষ ধ্বংসের কারণ জলবায়ু আর বাংলাদেশ থেকে মানুষ ধ্বংসের কারণ আওয়ামীলীগ আর আপনি সেই আওয়ামীলীগের মেকানিক।,0,celebrity
আপনি বেচেঁ থাকলে বেচেঁ থাকবে বাংলাদেশে অসংখ্য পাঠক।,0,celebrity
আপনার এই লিখাকে ধিক্কার না জানিয়ে থাকতে পারলামনা স্যার।,0,celebrity
৭১ এর কোদাল নিয়ে 🐄🐄আবার গর্জে উঠেছেন।,0,celebrity
চমৎকার লেখা। কলম চলুক।,0,celebrity
শেষ রাতে স্যারের শুভ বুদ্ধির উদয় হইলো..আর বাচ্চারা তো তার গায়েবানা জানাজাও পইড়া শেষ করে ফেললো।।এখন যে কি হবে স্যারের?????,0,celebrity
স্যার বমি করার আগেই স্যারের মুখের উপর মতিয়া চৌধুরী ঢেলে দেওয়া হোক!!,0,celebrity
"রাজাকার শব্দটা আমার কাছে খুব বিশ্রী লাগে। কিন্তু দেশের সুস্থ মস্তিষ্কের এম,পি, মন্ত্রীরা আমাদের নামের পাশে রাজাকার ঝুলিয়ে দেও তখন আমরা সেই ঘৃণিত ""রাজাকার ""  শব্দটাকে নিয়ে প্রতিবাদ শুরু করি। দেশ স্বাধীনের সময় রাজাকাররা একে একে যেমন নির্যাতন আর বৈষম্য সৃষ্টি করেছিলো। কিন্তু তা নির্মূলের পর এখানও 'বৈষম্য ' শব্দটা আমাদের সমাজে রয়েই গেছে। যেমন কোটা  বৈষম্য।  কিন্তু আজ অব্ধি এই কোটা বৈষম্যের  বিরোধিতা  করায় সাধারণ ছাত্ররা হয়ে যায় রাজাকার! হায় কপাল!",0,celebrity
"স্যার,একদম ছোটবেলা থেকে আপনাকে চিনি, বাংলার বুকে একজন বুদ্ধিজীবী হিসাবে জানি, সেই থেকে  আপনার উপর প্রত্যাশাটা অনেক বেশিই থাকে সবসময় । বড় দেরি হয়ে গেছে আপনার ঘুম ভাঙতে । এমনকি এখনো আপনার অনেক ছাত্রছাত্রীদেরকে অন্যায় ভাবে মারা হচ্ছে, কিন্তু আপনি অজানা কোন শক্তির দ্বারা বলবৎ হয়ে প্রায় চুপ করেই আছেন বলা যায় ।  ভরসাটা কমে যাচ্ছে স্যার আপনার উপর , দুঃখ জনক হলেও বলছি আপনার উপর শ্রদ্ধটা অনেক কমে যাচ্ছে ......  :-(",0,celebrity
"অসাধারণ বাস্তব কথা ,দোয়া করি বাকি দিন গুলো যেন ভালই কাটে ॥",0,celebrity
"স্যার আপনি স্টেটাস দিলে কমেন্ট পড়তে পড়তে আধা ঘন্টা কাটাই ফেলি অথচ লাস্ট কবে আপনার স্টেটাস পড়ছি মনে নাই! 😬 স্যার আপনার লম্বা কলামগুলা পড়তে বড্ড  আলসেমি লাগে! আরো ছোট করে লেইখেন, দেখি পড়ার ধৈর্য্য পাই কিনা!! 😜😜😂",0,celebrity
সাধারণ ছাত্রছাত্রীরা বুঝে গেছ আপনি কার পা ছাটা কুকুর।  আপনি হড়হড় করে বমি করবেন কিন্তু ছাত্ররা আপনার মুখে মুতে দিতে ড্রোন নিয়ে রাউন্ড দিচ্ছে।,0,celebrity
* বিনা ভোটে নির্বাচিত হয় একটা দেশের সরকার | আপনার কলম চলে না ?  * পুলিশ নির্বিচারে দেশের জনগনকে গুলি করে মারে | আপনার কলম চলে না ?  * নিরীহ বিশ্বজিত্‍ নামক এক যুবককে প্রকাশ্যে রাম দা দিয়ে ছাত্রলীগ জবাই করে  |আপনার কলম চলে না ?  আফসোস আমরা এমন একজন বিঞ্জানী পেয়েছি যে নিজ দলের পাঁ চাটতেই ব্যস্ত |  আমরা কি এমন একজনকে পাব না যে নিরপেক্ষ ভাবে দেশকে ভালবাসবে ? আফসোস থেকেই গেল ....,0,celebrity
আপনার এই প্রশ্নের জবাব দেবার কেও নাই স্যার...,0,celebrity
"এইলোকটাই প্রশ্নফাঁসের বিরুদ্ধে,সমন্বিত ভর্তি পরীক্ষার জন্য কথা বলে মুখে ফ্যানা তুলে ফেলেন।চাপাতির কোপ খেয়ে কোনোমতে বেঁচে ফিরেন।কাদের জন্য করেন স্যার এগুলা?আমরা সব ভুলে যাই।আপনি ট্রেন্ড বুঝেন না। পোলাপান ট্রেন্ড বোঝে। তাই অযথা গাইল খান।সময়মত একটা লেখা না লিখে এরকম গাল খাওয়া লাগে তা এইখানে না দেখলে বুঝতাম না।মানুষের উপকারের কথা আমরা মুহুর্তে ভুলে যাই।",0,celebrity
মরা মানুষ কথা কয়।ক্যামতে কি?,0,celebrity
হায় হায় ! কমেন্ট পইড়া আমিতো বেহুশ 😂😂😂😂 স্যার গো আপনি ক্যারে লিখতে গেলেন এসব পুঁথি ! আহারে !!😂😂😂,0,celebrity
স্যার আমরা গণিতের মজা করতে চাইলেও অনেক বাধা,0,celebrity
"স্যার, যতদিন আমরা আর আপনার জন্য আমাদের অন্তরে এই অসীম ভালোবাসা আছে ততদিন পর্যন্ত মহান রব আমাদের এতোগুলো মানুষকে কষ্ট দিয়ে আপনাকে নিয়ে যাবেনা! আমরা আমাদের পরম ভালোবাসায় আপনাকে আগলে রাখব স্যার!! ❤❤",0,celebrity
হারামজাদা কমেন্ট পড়ে না আবার ফটো কমেন্টের অপশন বন্ধ করে রাখছে 🤬,0,celebrity
শুভ সকাল স্যার।।,0,celebrity
কমেন্ট পড়ো 😆😆🔫🔫 Rina Munni Nishat Nishu,0,celebrity
"এতদিন কোথায় ছিলে.? ওই ঝরনা কে প্রশ্ন করো, ওই নদীকে প্রশ্ন করো, এতদিন কোথায় ছিলাম.. 🐸🐸",0,celebrity
মুক্তিযুদ্ধ দিয়া আর কতকাল খাইবেন,0,celebrity
আর যখন ক্রসফায়ার এর নামে মেধাবী ছাত্র নিহত হয় তখন আপনার এই দরদ কোথায়ামিন থাকে????,0,celebrity
হুম ঠিক বলছেন। সবার বাবা মা সার্পোটিভ হয় না। বরং অন্যের সাথে তুলনা করে তাদের অনেক অপমান করা হয়। এখন রেজাল্ট দিলেই কেউ আর বলে না পরের বার ভালো করবা। অনেকে তাই সুইসাইড করে ফেলে। মেধা নয় নাম্বার টাই সবাই দেখে।,0,celebrity
স্যার আপনার এই লিখার কোনো valu আমি খুঁজে পেলাম না। সরকারের তুসামোদি করা ছাড়েন আর ন্যায়ের কথা বলেন। তরুনরা ততো আর এমনি এমনি রাস্তা অবরোধ করে নাই। এখন দেখতেসি হুদাই মানুষ আপনাকে সম্মান করে। ধুরররর,0,celebrity
"""ব্রেকিং নিউজ""অবরোধের কারনে কাল কেরভালোবাসা দিবস স্হগিত করা হয়েছে।আগামী ৩০ তারিখভালোবাসা দিবস ঘোষনাদিয়েছেন প্রেম মন্রী।",0,celebrity
"স্যার নামাজ পড়ে দোয়া করুন, যাতে পুতিনের হাতে রাকিটিসের পরিবার জিম্মি না হয়😎  দুই রাকআত নফল নামাজ শুধু😜😎",0,celebrity
"এখানে বিনোদন চলে, কেউ মুহাম্মদ জাফর ইকবালকে আস্তিক প্রমাণ করতে ব্যস্ত, আবার কেউ নাস্তিক প্রমাণ করতে ব্যস্ত, বিনোদনটা ভালই উপভোগ করতেছি, শুধু দেখবো, আর আহরণ করবো",0,celebrity
উদ্ভট বুদ্ধিজীবি,0,celebrity
স্যার কি হবে এত লিখে।  কিছুই তো পাইবেন না :p,0,celebrity
"আপনি অনেক জ্ঞ্যানী মানুষ স্যার। আপনার বক্তব্যের সাথে দ্বিমত করা মানে ইদুর হয়ে সিংহের সামনে দাঁড়ানোর দুঃসাহস করার মত। আমার ছোট্ট হৃদয় সে দুঃসাহস দেখানোর মত উপযুক্ত নয়। কিন্তু, বইটি পড়ে আজ আপনার শুধু মন খারাপ হয়েছে কিন্তু কয়েক বছর পর যদি দেখেন যে নতুন প্রজন্ম আমাদের মহান মুক্তিযুদ্ধের 'ডেপুটি চিফ অফ স্টাফের' লেখা আপনার 'মন খারাপ করে দেওয়া' বই থেকে রেফারেন্স দিচ্ছে তাহলে আপনার মনের অবস্থা কিরূপ হতে পারে স্যার? নতুন প্রজন্ম যদি ভুল ইতিহাস জানে তাহলে এর দ্বায়ভার এড়ানো যাবে কিভাবে স্যার? ",0,celebrity
"আসসালামুআলাইকুম sir, দুইটা কথাই বলব ।  ১. এইদেশের শিক্ষা ব্যবস্থা নিয়ে যতই মাতামাতি করেন না কেন, রাজনৈতিক কোন্দলে সব প্রচেষ্টা ব্যর্থ পর্যবসিত হবে ।  ২. আর যদি সমন্নিত পরীক্ষা পদ্ধতি চালু করলেও যাকে আমি সাধুবাদ জানাই আপনি কি মনে করেন এখন ভর্তি পরীক্ষার নামে ছাত্রদের যেই রকম অত্যাচার করছে শিক্ষকেরা, তখন নতুন এই পদ্ধতিতে ছাত্র ছাত্রীদের কষ্ট করতে হবে না । তখনো দেখা যাবে ঠিকই শিক্ষকেরা নতুন কোন পদ্ধতিতে ছাত্র ছাত্রীদের কষ্ট দিচ্ছে ।  ",0,celebrity
এতগুলো মানুষের ভালোবাসা খোদাকে বাধ্য করবে,0,celebrity
With U,0,celebrity
হায় আল্লাহ কমেন্ট পড়তে পড়তে রাত ভোর হয়ে যাবে,0,celebrity
স্যার আপনি সুস্থ হয়ে আমাদের মাঝে ফিরে আসুন <3,0,celebrity
"জাফর ইকবাল, মুক্তিযুদ্ধের 'বিকৃত চেতনা'কে মূল্যবান প্রোডাক্ট হিসাবে সফল বাজারজাতকারী",0,celebrity
www.facebook.com/eibangla,0,celebrity
আমাকে অন্তত কিছু কমমেন্ট পড়ার জন্য হলেও আপনি মাঝে মাঝে কিছু আর্টিকেল লিখবেন,0,celebrity
আজ মঙ্গলবার 😑,0,celebrity
"মাননীয় স্যার   আপনি নারী, আপনার বউও নারী আমাদের প্রধানমন্ত্রী নারী, স্পীকার ও নারী আমার ঘরে একটা ভাংগা ক্যাসেট অনবরত বাজতে থাকে সেটাও নারী।   নারীদের জন্য সব কিছু হওয়ার পরও নারী পুরুষ সমান।   সুতরাং,  পুরুষ + জাফর স্যার = নারী পুরুষ সমান",0,celebrity
"আপনি ছাত্রদের কোন বিষয় কথা বলার আগে ভেবে নিবেন, কারন ছাত্রসমাজ আপনাকে ২ পয়সা দামেও মূল্য দেয়না...",0,celebrity
"অন্যান্য লেখকদের দেখা হয় যেভাবে :তাদের কবিতা,উপন্যাস,প্রবন্ধ ইত্যাদি সৃষ্টিকর্মের দ্বারা।    লেখক জাফর ইকবালকে বাঙালী দেখে যেভাবে :-অাস্তিক নাকি নাস্তিক,কোন রাজনৈতিক দল করে,দালাল নাকি চাটুকার,যোদ্ধা নাকি শান্তিপ্রিয়,গোফওয়ালা নাকি গোফছারা,কালা নাকি ফর্সা,শিক্ষক নাকি বিজ্ঞানী,বাদ যায় না পরিবার,গোষ্ঠি,অাত্মিয়স্বজনও।    Rip বাঙালী,বাঙালী পারেও বটে!",0,celebrity
আপনার এতোবড় রচনা পড়ার টাইম নেই আমার...যাই কাথা মুড়ো দিয়া ঘুম দেই কাজে দিবে :-D,0,celebrity
যাদের জাফর ইকবালকে নিয়ে এত চুলকানি তাদের এমবি খরচ করে তার পোস্টে হা হা রিঅ্যাক্ট বা কমেন্ট করতে আসার দরকার কী? তারা তো জাফর ইকবালের চেয়ে অনেক বড় জ্ঞানী!,0,celebrity
"স্যার আপনার অনেক কিশোর উপন্যাস পড়েছি। আরো পড়তে পারলে ভালো হতো কিন্তু আমি এখন যুবক! তাই আপনার কাছে বিশেষ অনুরোধ, কিশোর উপন্যাসের পাশা পাশি যুবকদের জন্য এবার নতুন কিছু লিখুন।।",0,celebrity
ষ্যাড়ে কয় কী!!! Md Saiful Islam,0,celebrity
"স্যার পোষ্ট করিয়া প্রমাণ করিলেন, তিনি মরেন নাই!",0,celebrity
"নিজের বাচার জন্য নীলক্ষেত চুল কাটতে যাওয়া লোকটা আমাদের মুক্তিযোদ্ধের গল্প শোনায়,রাজাকারের সংজ্ঞা শেখায়,আর কোটা সংস্কার আন্দোলনকে কোটা বিরোধী আন্দোলন বানায়। হাস্যকর বটে।",0,celebrity
এসব বন্ডামির জন্য বিচার হওয়া উচিত।  কোথা হতে আসছেন?   আজাইরা একটা গল্প নিয়া।  দুর হ শয়তান। বন্ড।  বাকওয়াজ।,0,celebrity
সত্যিই এখন গলায় আংগুল দিয়ে ভুমি করতে ইচ্ছা করছে।ফ্যাক্ট>জাফ্রিক বালের হুশ আইছে।,0,celebrity
"একজন তরুন লেখকের কথা চিন্তা করলে কষ্ট হচ্ছে, আবার 'মুক্তমনা' ভাব্লে ঘৃণা হয়। আমার একটায় প্রশ্ন, জীবন  মরণ সব ই সৃষ্টিকর্তার হাতে। অভিজিত কে সৃষ্টিকর্তা তার কাছেই নিয়ে গেছেন, সেটা তার দোষ হোউক আর নাই হউক। প্রশ্ন এটাই যে, আভিজিত হিন্দু ধর্মাবলম্বী, তার স্ত্রী মুসলিম জাতি। যদি তিনি ধর্মকে নিয়ে কটুক্তি করেন, তবে তার স্ত্রী কেন তাকে বাধা দিতেন না, তিনি কি ঊল্টো তাকে উস্কানি দিতেন? নাকি তিনিও মুক্তমনা ছিলেন। এত কিছু হউয়ার পরও তার স্ত্রী কিভাবে মেনে নিত?",0,celebrity
এই দেশের শিক্ষার্থীদের জন্য শিক্ষকদের কোন মায়া দয়া নাই।শিক্ষকদের অমানবিকতা পুলিশের গুলির চেয়েও ভয়ংকর!,0,celebrity
"আপনার লেখা থেকে কমেন্ট পড়তে বেশি আনন্দ লাগে।আফসোস হয়, হয়ত আপনি চেয়েছিলেন যুদ্ধের সময় ঘরে বসে বসে নজরুল হতে কিন্তু পাবলিক সেটি দেয় নি😉",0,celebrity
স্যার সত্যি বলতে এত বড় লিখাটা পড়ার মত ধৈর্য্যটা ধরে রাখতে পারলাম না। আপনি এত পরে রেসপন্স করবেন সেটা ভাবতে কষ্ট হচ্ছে। দেরিতে হলেও পক্ষে থাকার জন্য ধন্যবাদ আপনাকে স্যার।,0,celebrity
শুভ কামনা স্যার।,0,celebrity
"ইকচুল আংকেল বেঁচে আছেন,সবাই বলো ইকচুলগো 😃",0,celebrity
আপনার প্রতি অনেক শ্রদ্ধা ছিলো। কিন্তু আপনি এর যোগ্য নয়।,0,celebrity
বৃদ্ধ একটা মানুষকে যে আপনারা এভাবে অপমান করছেন আসলে সেটা টিক না।যতই যাই হোক উনি একজন সম্মানিত মানুষ আর বাংলাদেশ এর প্রথম শ্রেনীর নাগরিক।,0,celebrity
খুব ভাল লেগেছে!!!  এক নিঃশেষে পড়ে শেষ করলাম!!!,0,celebrity
"তুই আর কী বলবি দাদা,,তুই তো গর্তের ভেতর থেকে যুদ্ধ করছিলি",0,celebrity
প্রিয় লেখকের কলামের পাঠক প্রতিক্রিয়া একটু পড়িও লিজা। দেখো হাসতে হাসতে সুস্থ হয়ে উঠবা।  Farjana Liza,0,celebrity
"নারী পুরুষের সমান অধিকার অবশ্যই কাম্য। সবাই পড়াশোনা করবে সবাই স্ব স্ব ক্ষেত্রে ভূমিকা রাখবে। তবে, বর্তমানে আমাদের শিক্ষা ব্যবস্থা খুবই ভঙ্গুর হয়ে পড়ছে। অনেক বড় বড় ডিগ্রি বের হচ্ছে কিন্তু মানুষ বের হচ্ছে না।",0,celebrity
"এক চোখা মানুষ, ।।।",0,celebrity
আমার ভষা নেই । আমি বোবা হয়ে গেছি। চলমান পরিস্তিতি আমাকে কবোর দিবে।,0,celebrity
নিজের ছেলেমেয়েরে বিদেশে পড়ান। আমরা বিদেশি কারিকুলামে পড়লেই যত চুলাকানি? বাংলা পড়ে পোলাপান কি পরিমান মারা খাইতেছে সেটা আপনিও জানেন আমরাও জানি।পারলে শিক্ষা ব্যবস্থা পরিবর্তন করার জন্য ট্রাই করেন নাইলে চুপ মেরে বসে থাকেন। মেয়ে ফ্যানদের প্রসংসা কুড়িয়ে আর কতদিন? এবার কিছু করবার পালা। চলেন নামাজ পড়ে আসি 😁,0,celebrity
"নীল মিয়া বলেন, চার- সরকার একটু কৃপণ অ সঠিক হিসাবে চলতে পারলে  দেশের অনেকটাই অর্থ অভাব দুর হবে!  :---------------: ভালোবাসার খুঁজে",0,celebrity
সবটা না জেনেও কথা বলাটা এক ধরনের বোকামি -- সবাই সেটা বুঝে - অথচ আপনি সেটা বুঝলেননা --,0,celebrity
You are a great scientists and we some nobel man as like you.  May you live long.,0,celebrity
রাজাকারের নাতি জাপর কেমন আছো?,0,celebrity
"আমি একবালের স্ট্যাটাস পড়িনি,  তবে কমেন্ট পড়েই নববর্ষের আনন্দ পাইলাম 😂😂",0,celebrity
"আপনি সারা জীবন  অনেক অন্যায়ের বিরুদ্ধে লিখেছেন। দেশের জন্য ত্যাগও স্বীকার করেছেন। কিন্তু জীবনের শেষে ভুল সিদ্ধান্ত (ছাত্রদের মতে)গ্রহন করে আজ ছাত্র সমাজের কাছে সার্থপর হিসেবে গৃহিত। এখানে আপনার ভুল নেই কারন টিকে থাকতে সবাই চায়। আপনার টিকে থাকাকে সাধুবাদ জানাই।  শুধু একটাই কষ্ট শামসুজ্জোহা স্যারের গল্প শুনে যারা আপনাকে তার কাতারে রেখেছে সেই সকল ন্যাড়ারা বড়সর ধরা খেয়ে বেল তলা থেকে ফিরেছে।   আপনি আসলে সেই কাতারের না। আপনি বর্তমানের মেধাবী,নিষ্ঠাবান,রাজনৈতিক শিক্ষক,ভাল লেখক,.......।   তবে আপনি চাইলেই হতে পারতেন সেই শিক্ষক যাকে না দেখেই লিখা পড়ে ভক্ত হয়েছিলাম।ভেবেছিলাম তার হাত মাথায় রাখতে পারলে, তার পা ধরে সালাম করতে পারলে জ্ঞানের পূর্নতা পাবে।",0,celebrity
ষ্যাড়ে উপর যে হারে বমি হচ্ছে দেশেতো বমির বন্যা বয়ে যাবে।,0,celebrity
আমরা কি আর কখনো এই নোংরামি থেকে মুক্তি পাব?,0,celebrity
"দালালী কত প্রকার ও কি কি সেটা আপনাকে না দেখলে বোঝা যাবেনা।  রক্ষীবাহিনী কার গড়া? মুজিবের গড়া বাহিনী।সেই বাহিনীকে নিয়ে আপনি কি লিখেছিলেন মনে আছে?  ""রক্ষীবাহিনী নাকি আপনার বিধবা মাকে সরকারিভাবে বরাদ্দ করা বাড়ি থেকে উৎখাত করে সত্যিকার অর্থে পথে নামিয়ে দেয়"" ( রক্ষীবাহিনীর সত্য- মিথ্যা পৃষ্ঠা নং ৯৪) এগুলো রসিয়ে রসিয়ে লিখতে পারেন আবার ফেবুতে এসে দু'মুখো সাপের মত রুপ ধারন করেন? লজ্জা করেনা?  সেদিন মুজিবের গড়া বাহিনী নিয়ে এমন মন্তব্য করেছিলেন আজ আসছেন মুজিবের প্রশংসা করতে? চাটুকার কোথাকার! 😂😂",0,celebrity
কমেন্টগুলো তে লাইক বেশী.... :P,0,celebrity
"স্যার, আপনি ভাল আছেন শুনে খুব ভাল লাগছে। আপনার আঘাতের খবর শুনে আমার খুব খারাপ লেগেছিল কিন্তু এখন ভাল লাগছে। আপনার মত মানুষকে হারাতে চায় না বাংলাদেশ।  আপনি আমাদের দেশের গৌরব। আপনাকে দেখে দেশের কত অমানুষ মানুষ হয়েছে তা আপনি নিজেও যানেন না। আর সেই অমানুষদের মধ্যে আমিও একটা। আপনাকে দেখেই আমি মানুষ হচ্ছি। আরো হবার আশায় আছি।  ভালবাসা আপনার জন্য স্যার, ভাপ থাকবেন।",0,celebrity
"বন্ধু ১বাল-  তুমি বাংলা ছবি শেষে আসা পুলিশের মত, সব কিছু যখন শেষ হয়ে যায় তখন আস। এ ভন্ডামী আর কতদিন করবা.. কতদিন করবা চামচামি?",0,celebrity
স্যার মদ খাবেন সত্য লিখবেন#,0,celebrity
"(চ) নং আলোচনার ব্যাপারে একটা কথা বলি, স্যার, শুধু নিচু ক্লাস এর student রা নয়, আমরা উঁচু ক্লাস এর student রাও পরীক্ষার যন্ত্রণায় মরমর  :(  বিশেষত আমার মত যারা পড়াশোনায় অমনোযোগী !",0,celebrity
কমেন্ট গুলা পড় Mishal Ahmed Nil Ahamed Arafat Hossain Nm Masum,0,celebrity
"উনি জিন্দা হয়ে উঠেছিলেন!  কিন্তু কমেন্ট গুলা পড়ার পর মদ খেয়ে আবার মরে গেছেন। 😊  আল্লাহ, তারে জান্নাতবাসী করুন। আমীন। ✌✌",0,celebrity
"জাফর স্যার,  আপনাকে আমি ব্যক্তিগত ভাবে খুব পছন্দ করি।  আপনাকে আমি মুক্তচিন্তক,  এবং সমাজ নিয়ে ভাবুক মনে করি। এক কথায় বুদ্ধিজীবী আপনার নামের সাথে যোগ করি।  কিন্তু আজ আপনার এই লেখাটি পড়ে হতাশ।  আপনি ভালো শিক্ষক এবং সাথে খুব ভালো লেখক,  আপনি ছাত্রদের বুঝতে ভুল করবেন এটা মানতে পারছি নাহ।   রাজাকার শব্দটার সাথে শিশুকাল থেকেই পরিচিত,  শুনলেই চোখের সামনে ভেসে ওঠে ১৯৭১ এর জুলুম,স্ব -দেশী কিছু বিশ্বাসঘাতক হীন মানবের চিত্র।  কিন্তু দুঃখের সাথে বলতে হয়,  আমাদের এক মন্ত্রী এই ঘৃণ্য শব্দ টা ছাত্রদের ক্ষেত্রে ব্যবহার করেন।  আমরা ছাত্ররা কোন ভাবে রাজাকার???  ন্যায্য দাবী করেছি বলে,  নাকি দেশের শিক্ষিত বলে অন্যায়ের বিরুদ্ধে চুপ করে থাকতে পারি নি বলে!  তখন প্রতিবাদের ভাষা হিসেবেই ""আমি রাজাকার "" লেখা গায়ে জড়ায়।  ওটা গর্বের ছিলো নাহ,  ওটার প্রতিটা অক্ষর ছিলো লক্ষ লক্ষ ছাত্রের প্রতিবাদ।    রাস্তা যাকে আমরা রাজপথ বলি,  এটাও আপনাদের ই শিখানো বুলি।  রাজপথ আটকে দেশকে অচল না করা পর্যন্ত দেশের প্রধানের কানে পানি যায় নাহ,  এটা ও আপনাদের দেখানো পথ।    আমরা শান্তিপূর্ণ ভাবে আন্দোলন করেছি এবং আমরা করব.... আমরা বড় দের দেখানো আগুন জালো বা ভেঙে মানুষদের ক্ষতি করার চর্চা করিনি এবং করবো নাহ। তবু ও সরকার আমাদের উপর অনেক নির্যাতন করেছে,  হয়েছে  আমাদের ভাই বোন  আহত। আর ভিসির বাড়িতে কে বা কারা আক্রমণ করেছে তা জাফর স্যার আপনার বুঝতে কষ্ট হবার নয়।  আপনি ও একদা এই রকম শিক্ষকদের অবমানোনার ঘটনা নিজ চোখে দেখছেন।  তাই বলবো,  একটু ভাবুন।  ভুল ভেবে এই আন্দোলনরত ছাত্রদের  ঘৃণা করবেন নাহ।    আপনার জন্য ভালোবাসা।",0,celebrity
"স্যারের নামে বদমান করবেন না,উনিই একমাত্র মানুষ যিনি মরার পর ও ছাত্র-ছাত্রীদের কথা ভেবে স্ট্যাটাস দেয়.",0,celebrity
"আমি এক ফেরিওয়ালা ভাই, চেতনা ফেরি করে বেড়াই। আমার চেতনা কিনতে হলে  আস্ত পাগল হওয়া চাই।",0,celebrity
অওও মাহ গলু গলু 😣😣😣😣 খিল মিহ্ 😫😫,0,celebrity
"আমি ""মির জাফর""কে দেখি নি,আমি আপনাকে দেখেছি।😏😏😏",0,celebrity
স্যারের পোষ্ট নাপড়ের কমেন্টে এলাম।কিছু মজা নেওয়ার জন্য।,0,celebrity
"স্যার, আপনার পোষ্টে কমেন্ট করতে করতে আর পড়তে পড়তে আজ আমি ক্লান্ত! আঝ আড় কমান্ড কড়ার বাশা কোজে পাচ্চি না! 🐸🐸",0,celebrity
একজন শিক্ষক কত দ্রুত একজন ছাত্রের মন ভালো করে দিতে পারে আপনি তারই প্রমান। আপনাকে নমস্কার।,0,celebrity
অাপনার উচিৎ ছাত্রদের অভিবাবক হিসাবে তাদের সাথে একাত্বতা প্রকাশ করা,0,celebrity
আপনি আপনার চুরি করা ইংরেজি গল্পের বই বাংলায় ডাবিং করা ১০০০ বছরের ঘুমন্ত উদাহরন। ক্যাপসুল থেকে বের হয়ে ঘুম ঘুম চোখে কি সব কইলেন আপনিই জানেন,0,celebrity
স্যার আপনি সুস্থ হয়ে ফিরে আসুন আমাদের মাঝে। ঈশ্বরের কাছে এই প্রার্থনা করি,0,celebrity
"আমার মতে , বাংলাদেশের স্কুল কলেজের ম্যাক্সিমাম ভাল ছাত্রগুলো নেয় সাইন্স । তাদের মধ্যে অধিকাংশই  ইংরেজিতে ট্রাই ই করে না । আর দ্বিতীয় শ্রেণীর ছাত্ররা নেয় কমার্স । তারাও ইংরেজিতে ট্রাই করে বলে মনে হয় না । আর যারা পাশ ফেল নিয়ে টেনশনে থাকে তারা নেয় মানবিক । , তো ইংরেজি বিভাগের এমন দশা তো হবেই ।",0,celebrity
এখন সেই ইংরেজি দৈনিক এবং খুবই জনপ্রিয় নিউজ পোর্টালের কাজ এই লেখনীর বিপরীতে মন্তব্য গুলো তুলে ধরা।।।।নইলে বুঝবে কিভাবে!!!!,0,celebrity
সবার কমেন্ট দেখে আমার হরহরিয়ে বমি করে দিতে ইচ্ছা হচ্ছে,0,celebrity
ওয়াক করে বুমি আসে!! স্যার এতো ভোরে বুমি করছেন কেনো?,0,celebrity
"হ্যালো স্যার, আপনি বেঁচে থাকবেন, আপনার বেঁচে থাকাটা খুবই জরুরি। আমাদের দোয়ায় আপনি বেঁচে থাকবেন।।",0,celebrity
"স্বাধীনতা অর্জনের চেয়ে স্বাধীনতা রক্ষা করা কঠিন । আমি মুক্তিযুদ্ধ নিয়ে তর্ক করবো না । কারন আমি সেই সময়ে জন্মি নি । ইতিহাস ঘেটে যতদুর জানি মুজিব, আওয়ামি লীগ, জিয়া, বিএনপি জামাতের প্রতিষ্ঠিত হওয়া, তাদের ভালো খারাপ ও রাখি । এবার আসেন বর্তমান নিয়ে । এই যে কুলাঙ্গার ছাত্রলীগ, আর আওয়ামি শঠ, মিথ্যা, বানোয়াট, চোর যারা গনতন্ত্রের নামে জোর ক্ষমতাসীন থেকে দেশ কে চিবিয়ে চিবিয়ে খাচ্ছে, তা কি কারো চোঁখে পড়ে না ? আপনার চোঁখে না পড়ুক, হাজারো তরুন প্রজন্ম আছে, তাদেরকে কতদিন মিথ্যা ইতিহাসের দোহাই দিয়ে থামিয়ে রাখবেন ???",0,celebrity
আমি এস.এস.সি পাশ করছি এক অজপাড়া গায়ের স্কুল থেকে।এখন আমি ঢাকার মাইলস্টোন কলেজে ২য় বর্ষে পড়ি। ক্লাসের সবচেয়ে কম জিপিএ আমার।ক্লাসে অনেক জিপিএ৫ আছে যারা প্রত্যেক সাময়িক পরীক্ষায় দুই তিন সাবজেক্ট এ ফেইল করে কিন্তু আমি কোন সাময়িক পরীক্ষায় ফেইল করিনি।কিন্তু যখন স্যার বা অন্য কেউ জিজ্ঞেস করে জিপিএ কতো তখন লজ্জায় মাথাটা নিচু হয়ে যায়।অনেকে যখন বলে জিপিএ৫ আর আমি যখন বলি ৪.৫৬ তখন নিজের যে কেমন লাগে বুঝানোর মতো নয়।,0,celebrity
স্যারের নানা নাকি মুক্তিযোদ্ধা ছিলেন???,0,celebrity
জাফর স্যার আপনি মানুষ হন,0,celebrity
"বাংলাদেশে কয়েকটা ভার্চুয়াল মানসিক কেন্দ্র খোলা দরকার। কমেন্ট সেকশনের আবালগুলা সেখানে ভর্তি হবে। ভাইসকল, পারলে স্যার এর সামনে গিয়ে বলেন। এত্ত কথার একটা কথাও যদি এইভাবে বলতে পারেন, তাহলেই হবে। প্রতিদিন কমেন্ট করে কোনো লাভ করতে পারলেন?",0,celebrity
স্যার আপনার কাছে কিছু পপকর্ন থাকলে দেন কমেন্ট পড়তে বসবো 😜😜,0,celebrity
"আমরা' শব্দটি দিয়ে আপনি আজকে কোন দলে আসতে চাচ্ছেন বুঝা যাচ্ছেনা। দুইদিন অপেক্ষা করে যখন নিশ্চিত হলেন ইস্যুটাকে রাজাকারী ফ্লেভারে আনা যাচ্ছেনা, তখনই কি 'আমরা' হয়ে গেলেন? আপনি হোসেন মোহাম্মদ এরশাদকে চিনেন? আপনি জানেন কি আপনি এই কিংবদন্তীকেও ছাড়িয়ে যাচ্ছেন?  প্রথমে কোটা আন্দোলনলকে ন্যায্য বলে পরে যখন দেখেন ভাত জুটে না তখন রাতারাতি আন্দোলনকারীদের আপনি বানালেন রাজাকার। তারাই মার খেলো, তারাই রাজাকার হল, তারাই রিমান্ডে গেল। আপনি তখন তরুণ প্রজন্মের জন্য মুক্তিযুদ্ধের বই রচনা করছেন। সাধাসাধি গল্প। প্রয়োজনের সময় তরুণ প্রজন্মের হাত ছেড়ে আপনি ধরেছেন সরকারের রক্তপিপাসু হাত। জনপ্রিয়তা ধরে রাখতে আপনি আর কী কী করতে পারেন এর একটি তালিকা কি জনসম্মুখে প্রকাশ করা যায়? আমরা লাইক কমেন্ট দিতাম।  এইবার আপনার চোখে পানিও দেখলাম না। এই পরিস্থিতিতে চোখ শুকনা থাকলে হবে? বয়স বাড়ার সাথে সাথে সরকারের মত আপনিও ভুল করা শুরু করেছেন একের পর এক।   আপনার কাছে স্যার আমার একটা ব্যক্তিগত আর্জি আছে। মাটির সত্তুর ফুট নিচ দিয়ে চলে এমন একটি ড্রোন বানাবেন। ড্রোনের লেজটা দিবেন টিকটিকির মত। ড্রোনটির এক কপি আমার জন্যও রাখবেন। মাটির উপরে আপনার মত জীব যে দেশে আছে আমি ওই দেশে মাটির নিচ দিয়েই চলাচল করতে চাই।",0,celebrity
স্যার এরকম উল্টাপাল্টা লেখা আপনার হতেই পারে না! তাড়াতাড়ি আরেকটা পোস্ট দিয়ে বলুন আপনার আইডি হ্যাক হয়েছিল। কি করবেন থাক সে কথা। এখন বলুন মতিয়া আপা আপনাকে কি যাদু করেছে যে আন্দোলনকারী ছাত্রছাত্রীদের রাজাকার বলার পরও উনার গায়ে বমি করলেন না!!! মতিয়া চৌধুরী মুক্তিযোদ্ধাদের অসম্মান করল আর আপনি তাকে সাপোর্ট দিয়ে ছাত্রছাত্রীদের গুষ্ঠিউদ্ধারে লেগেছেন!! মহানমুক্তিযুদ্ধের সময় আপনি টগবগে যুবক। যুদ্ধ না করে পালিয়ে বেড়াইছেন। লজ্জা করা উচিত্‍ আপনার। ছোটবেলা থেকেই আপনাকে সম্মান করি। বড়াই করে বন্ধুদের কাছে আপনার গল্প করি। এখন বন্ধুদের কাছে আপনাকে কি বলে পরিচয় দেব?? দালাল বলে!!,0,celebrity
লোকটার পিছনে সবাই এমন ভাবে লাগছে কোনো কিছুতেই তারে তুলাধুনা করা ছাড়ে না...😂,0,celebrity
সুস্থ মস্তিষ্ক আর সুস্থ মনোবল গঠনে আপনাকে এই বাংলা চাই.... বেচেঁ থাকতেই হবে এই বাংলায় .... ভালোবাসি স্যার,0,celebrity
"সালাম স্যার, আল্লাহর কোটি, কোটি শুকরিয়া আপনার সুস্থতার জন্যে, আল্লাহ আপনাকে এই অবিশ্বাস্য সুন্দর পৃথিবীটিকে আরো অনেকদিন ধরে দেখার সুযোগ দিয়েছেন। আপনার প্রতি আমার বিনীত আবেদন , এই যে সুযোগটা আল্লাহ আপনাকে দিয়েছে  এই সুযোগটার কিছু সময় হলেও আল্লাহর জন্য দান করে দিন, আল্লাহর দেয়া জীবনবিধান পডুন, জানুন, লিখুন, আপনার মতো এতো বড শিক্ষিত ও ক্রিয়টিভ মানবের জন্য শিক্ষা অনেক সহজ হবে। আল্লাহ হয়তো আপনাকে আল্লাহর শুকরিয়া আদায়ের সুযোগ করে দিলেন। আমার দোয়া আপনার জন্যে আল্লাহ যেন আপনাকে সত্যের উপর বাকি জীবন কাটিয়ে দেয়ার ভালো সুযোগ করে দেন। আল্লাহ আমাদের সবাইকে আল্লাহর দেয়া জীবনবিধান অনুযায়ী চলার পথ সহজ করে দেন। আ-মীন।",0,celebrity
"আমরা আপনাকে ভালোবাসি কারণ আপনি আমাদের মুক্তিযুদ্ধের প্রথম শিক্ষক। ভালোবাসি কারণ আপনি আমাদের শিখিয়েছেন মুক্তিযুদ্ধ নিয়ে কোন আপোষ হয় না, কোন দলবাজি হয় না। শিখিয়েছেন হয় তুমি মুক্তিযুদ্ধের পক্ষে বা বিপক্ষে, মাঝখানে কিছ নেই। শিখিয়েছেন স্বদেশপ্রেম সবার আগে, তারপর দুনিয়া।   ভালোবাসি আপনাকে স্যার। আমার মতো আপনার লাখো ছাত্র-ছাত্রীর দোয়া থাকতে আপনার কিছুই হবে না।",0,celebrity
বুকে হাত দিয়ে বলছি কখনো কোথাও কোচিং পড়িনি।আর তার ফলস্বরূপ সামান্য  মেধাবী হয়েও পিছিয়ে পরতে হয়েছে জিপিএ নামক স্কেলে।  ক্লাস নির্ভরতায় উচ্চমাধ্যমিক এবং অনার্স ক্লাস গুলোর সংখ্যা  হাত গুনে বলতে পারব।,0,celebrity
স্যার আল্লাহ আপনাকে অনেক দিন বাচায় রাখুক এই দুয়া রইল :),0,celebrity
"এই প্রথম ফেসবুকে 'Unlike' অপশনের অভাব বোধ করছি। আহ, আজ যদি Unlike অপশন টা থাকতো . . . 😢",0,celebrity
একটা সবুজ পৃিথবী এখনও সম্ভব!!,0,celebrity
"জাফর ষারদের পক্ষে নিতে বিশি কিছুর প্রয়োজন নেয় একটু আনন্দ ফুর্তির ব্যাবস্থা করলেই হল, আর সেই কাজটিই মনে হয় করা হয়েছে।",0,celebrity
স্যারের জন্য রয়েছে কেয়া কসমেটিকসের সৌজন্য গিফট হ্যাম্পার এবং সেই সাথে থাকছে বাছাইকৃত ৫০০০ সেরা জোকসের মুল্যবান বই সামগ্রী।,0,celebrity
আবুল মকসুদের মত বুদ্ধিজিবি দেশ সমন্ধে না বললেই ভালো কারন উনি নিজেই মরার আগে কাফনের কাপড় পরে মরে গেছেন বা তার চিন্তা বুদ্ধি মরে গেছে।এই দেশে যদি এতই সমস্যা তবে উনি এই দেশে আছেন কেন।,0,celebrity
"স্যার, সকাল থেকে বমি বমি ভাব হচ্ছে। এখনই কি হরহর করে বমি করে দেবো, নাকি আপনার স্ট্যাটাস পড়ে তার পর বমি করব জানালে কৃতজ্ঞ থাকতাম।",0,celebrity
শ্রদ্ধেয় স্যার আমরা কিন্তু খুব মাইন্ড করলাম   http://www.somewhereinblog.net/blog/mujahid419/30240110,0,celebrity
আমরা এই কুলাঙগার দের কাছ থেকে আর কি আশা করতে পারি?,0,celebrity
"শিক্ষানবিশ ব্যক্তি আপনি? 🙄 রাস্তায় বাচ্চাকাচ্চারা মরছে,আন্দোলন হচ্ছে আর আপনি কি ঘুমাচ্ছেন নাকি পেদেই চলছেন? 🙄",0,celebrity
"কীর্তিমানদের মৃত্যু হয় না স্যার। আপনি আছেন, থাকবেন।",0,celebrity
"জীবনে যদি কখনো, বই লেখার সৌভাগ্য হয়, তাহলে সর্বপ্রথম বামপন্থিদের নিয়েই লেখবো এবং বইটির নাম রাখবো 'ভূতের বচ্চা জাফর ইকবাল'",0,celebrity
কিছুই বলার নেই,0,celebrity
হড় হড় কইরা!!,0,celebrity
তোমার মুজিব ড্যাডি মুক্তিযুদ্ধ না করে পাকিস্হান পালিয়ে যায়। তোমার হাসিনা আপা ও গোটা মুজিব পরিবার যুদ্ধের সময় ১৫০০রুপি ভাতা খেতো পাকিস্হান সরকারের থেকে প্রতি মাসে।  সাহস থাকলে এগুলো নিয়ে কিছু বলে দেখাও দালাল জাফর। মুক্তিযুদ্ধ আর সংখ্যালঘুদের বিক্রি করে আর কত খাবিরে আম্লীগের বাচ্চা জাফর??!,0,celebrity
একটা কাঁচা বাঁশ ফাটিয়ে ঐ ফাটা অংশের মধ্যে তোর নুনুর দুইটি বিচি চেপে ধরে- তোর মুখে গণতন্ত্রের সংজ্ঞাটি শুনতে আমার খুব মন চাচ্ছে।,0,celebrity
"এ ভাবে শুরুতেই ২ নম্বর করার বিষয়টি একটি শিশু  অভ্যাস শুরু করে তাহলে , আমরা দুর্নীতি গ্রস্থ জাতি  হিসেবে বিশ্বে ১নং এ  থাকতে হবে সব সময়।",0,celebrity
#Goodidea!,0,celebrity
"হেতে জাতে মাতাল, তালে ঠিক।  বিষয়টা হাস্যকর!",0,celebrity
"স্যার, ""চুতমারানী"" শব্দের অর্থ বের করতে গুগলে সার্চ দিছিলাম। গুগল আপনার নাম বলে। কীয়্যাক্টাবস্হা!",0,celebrity
"ভোট শেষ বলে কি চেতনার কথা শেষ, স্যার? ""মুক্তিযুদ্ধের চেতনা"" শব্দটি ছাড়া আপনার লেখাগুলো বড্ড বেমানান।",0,celebrity
"জাফর সাহেব আপনি এযুগের নব্য রাজাকার। গুম হওয়া তরুণ ছেলেদের মায়েদের চোখের পানি, সন্তানের অভিশাপ আর স্ত্রীদের হাহাকার একদিন এদেশে আপনার মত মিষ্টভাষী জঙ্গির বিচার করবে। হুমায়ুন আহমেদ বেঁচে থাকলে বলতো জাফর তুই রাজাকারি বন্ধ কর. তুই রাজাকার জাফর তুই রাজাকার।",0,celebrity
যদি তুমি ভয় পাও তবে তুমি শেষ!  যদি তুমি রুখে দাড়াও তুমিই বাংলাদেশ! কিন্তু যদি রুখে দাড়িয়ে আবার চুপ হয়ে যাও  তবে তোমার চৌদ্দগুষ্টি শেষ!  সো! যদি বাচতে চাও তবে রুখে দাড়ানো বন্ধ করা যাবেনা যতক্ষন না জালিমের পতন হয়!  হে জাতি সিদ্ধান্ত নিতে হবে তোমাকেই  তুমি কি একা নিজে শেষ হবা! নাকি চৌদ্দগুষ্টি শেষ করবা!  না তুমিই বাংলাদেশ হবা!,0,celebrity
মন খ্রাপের ঔষধ অাপনার পোস্তের কমেন্ত গুলা.....  :-D :-D :-D :-D,0,celebrity
কি গালি দিবো? সবাই কেনো সব গালি দিয়া ফেলতাছে???????,0,celebrity
পোষ্ট না পইড়া খালি কমেন্ট পড়ি!!,0,celebrity
এক বা*দ ফেসবুক বানায় আরেক বা*দ লাইভ কি তাই চিনে না! পুরা দেশটাই বা*দে ভরে গেল!!!,0,celebrity
আপনাদের শৈশব অনেক সুন্দর ছিল,0,celebrity
এরপর কিছু মানুষ অন্যের কথাও স্যারকে দলকানা বলবে,0,celebrity
"""মানুষ যে কতো ভালো হতে পারে, কতো নিঃস্বার্থ আত্মত্যাগী হতে পারে, সেটা আমরা দেখেছি মুক্তিযুদ্ধের সময়।  আবার ঠিক একইভাবে মানুষ যে কতো খারাপ হতে পারে, কত নৃশংস এবং অমানুষ হতে পারে সেটাও আমরা দেখেছি মুক্তিযুদ্ধের সময়।""",0,celebrity
রাজাকার শাবকেরা যাই বলুক লেখাটা মুক্তিযুদ্ধ- এর চেতনাধারী একজন বলিষ্ঠ লেখকের। মতিয়া চৌধুরীর কোন ভুলের জন্য অনেক প্রতিবাদ হতে পারে কিন্তু কখনওই 'রাজাকার' শব্দটি নিজের অস্তিত্ব -  এর সাথে মিলাতে পারব না। ধন্যবাদ জাফর স্যারকে সময়োপযোগী একটি চমৎকার লেখার জন্য।,0,celebrity
"রচনাখানা অতি স্থুল বুদ্ধি প্রসূত । যাহোক, সিটি কর্পোরেশন নির্বাচন হল। দুই দল মনোনয়ন দিল দুই বকলমকে। পাবলিক নাচল তাদের নিয়ে । বকলম কি প্রকৃত সড়ক উন্নয়ন করতে পারে ।  দুর্ঘটনা সাথে  সড়ক উন্নয়নের সম্পর্ক আছে। সড়ক উন্নয়নের সাথে জড়িত আছে গনিত, পদার্থ বিজ্ঞান, সিভিল ইঞ্জিনিয়ারিং, নগর পরিকল্পনা, আর্কিটেক্ট ডিজাইন ---আরো আরো কত কি। বকলমের নেতৃত্বে কি  এগুলো সম্ভব !!!!!",0,celebrity
কমেন্ট পড়তে আইলাম ফ্রান্স😎😎😇😇,0,celebrity
স্যার আপনি কত নম্বর সেক্টরে মুক্তিযুদ্ধ করেছেন? আপনি বর্তমান বাংলাদেশের সবচাইতে ইম্পরট্যান্ট মুক্তিযোদ্ধা।  আপনাকে নিয়ে সামনের বিসিএস এ প্রশ্ন আসতে পারে।  কিন্তু স্যার আপনি কত নম্বর সেক্টরের মুক্তিযোদ্ধা ছিলেন সেই ডাটা কোথাও পাচ্ছিনা স্যার। দয়াকরে যদি একটু বলে দিতেন স্যার।,0,celebrity
চ্যাতনা আজ গাঞ্জার পুটুলিতে ষাঁড় 😒✌,0,celebrity
ইদানিং স্যারের পোস্টের শিরোনাম দেখেই চট করে কমেন্টের বাক্সে চলে যাই--- বড় অসাধু হয়া গেছি!ক্যানযে এমন হয়!!😜😜😜😜😜,0,celebrity
আপনার কিসের অভাব ছিল?????,0,celebrity
উনি কি মুক্তিযোদ্ধা!!!!!!!!!!!!!!!!!!!  কিন্তু ঐ সময় যুদ্ধে না গিয়ে পালিয়ে ঢাকায় এসেছিলেন!!!!!,0,celebrity
খুব মন খারাপ খুব?🙄🙄  কমেন্ট গুলান পড়ো তাইলে😂😂 Fahim Montakim ShihAb Rahman মন্দিরা সরকার Adittho Goswami Razdip Redowan Rabby,0,celebrity
"চলেন স্যার নামাজে যাই,আর লিখতে হবে না।",0,celebrity
"জ্বি! দেশের মানুষ বিজয় উপহার দিয়েছে। তারা এতোই খুশি যে, ভোট দিয়ে যেয়ে দেখে তাদের পছন্দের প্রার্থীকে ভোট দেয়া হয়ে গেছে, কষ্ট করে নিজের ভোট পর্যন্ত দেয়া লাগে নাই। সবাই খুশি মনে বাড়ি ফিরে গেছে।  হিরো আলমের মতো ফাতরা লোক নির্বাচন কেন্দ্রে ঝামেলা করতে চেয়েছিল তাকে সচেতন জনতা সেখান থেকে হটিয়ে দিয়েছে।  আর সোনার ছেলেরা ওই ৪ বাচ্চার জননীর সাথে লীলাখেলা করেছে তাদেরকে আপনি মাথায় হাত বুলিয়ে বুঝিয়ে বলবেন এমন দুষ্টুমী আর যেন না  করে - কেমন!  এমন সরকার এবং আপনার মতো বুদ্ধিজীবীরা থাকলে বাংলাদেশের সব ঘরে ঘরে নতুন শিশুরা ভুমিষ্ঠ হওয়ার সাথে সাথে কেঁদে ""জয় বাংলা"" বলে উঠবে ... !!!",0,celebrity
"একটা অমুক্তিযোদ্ধা পরিবারের কেউ কখনো ই বুঝবে না মুক্তিযোদ্ধা কি, এটা বাংলাদেশের রচনার এক ইতিহাস!  আর তাই এরা নিজেকে রাজাকার বলতে ও দ্বিধা করেনা!  বাংলাদেশের মাটিতে এই নব্য স্বঘোষিত রাজাকার ও এদের উতসাহ প্রদান কারী বিচার অবশ্যই করতে হবে!  এ দেশ মুক্তিযোদ্ধা দের, এদেশ মুক্তিযোদ্ধা প্রজন্মের দেশ!  অসাধারণ লেখা স্যার!  আপনার সবসময় মঙ্গল হউক!  জয় বাংলা জয় বঙ্গবন্ধু বাংলাদেশ চিরজীবী হউক!",0,celebrity
অতি উৎসাহীরাই ভোট চুরির উৎসবে মেতেছিলো স্যার! এগুলো না বুঝলে এতো ডিগ্রি নিয়ে কি হবে বলেন? 😆,0,celebrity
ভাগ্যিস মরে নাই মরে গেলে পরে বিনোদনের অভাবে গাজা খাওয়া শুরু করে দিতাম..,0,celebrity
৭১ সালের মুক্তিযুদ্ধে আপনার ভূমিকা কি? কোথায় ছিলেন তখন?  জানতে চাই?,0,celebrity
আমার মতো কে কে আছেন যারা পোস্ট না পড়ে কমেন্টস পড়ছেন? 👀🙌,0,celebrity
অাপনি বেচেঁ অাছেন তাহলে গতকাল কার জানাযা পড়লাম। অামি কে?😛,0,celebrity
কিরে জাফর,0,celebrity
"আই রিপিট বর্তমান সময়ের প্রেক্ষিতে,,,🙂 স্যার ,আপনার আর আমার পরিস্থিত একই শুধু পার্থক্য আপনি বর্তমান সেলেব্রেটি আর আমি ভবিষ্যৎ!!ব্যাপার হলো আমরা দুজনই  ঘুমে থাকি ।।😎 আজ টিউশনে যাওয়ার সময় দেওয়ালে লাগানো পত্রিকায় নিউজ টা দেখলাম।।ব্যাপার টা খুব উদ্বিগ্নের।। 😕 আপ্নারা এই পর্যায়ে এসে যদি এসব অসহায়ত্ব প্রকাশ করেন স্যার আমার তো বিয়েই হয় নি।। 🙃 (বাক্য ত্রুটি ক্ষমাশীল দৃষ্টিতে দেখবেন।।স্যার ভালো থাকবেন।।)",0,celebrity
স্যার আমাদের ছেড়ে চলে যাচ্ছেন,0,celebrity
কৌশলী লেখা 😉,0,celebrity
এখন হরহর করে বমি হয় না??,0,celebrity
আমার পক্ষ থেকে স্যারকে আন্তরিক অভিনন্দন।,0,celebrity
কোন জায়গা থেকে কপি করছেন আমিও করতে চাই🤓,0,celebrity
আমিও আপনার মা এবং বাংলাদেশের অসংখ্য মা'কে শ্রদ্ধা ও ভালোবাসা জানাই।,0,celebrity
"স্যার অনেকেই অাপনাকে ঘৃনা করে কিন্তুু কেন করে সেটা তারা নিজেরাই জানেনা! তারাই অপনাকে অপবাদ দেয় যারা কখনোই অাপনার লিখা পড়েওনা পড়তে পারেওনা, অামরা অাপনাকে ভালবাসি কারন অামরা জানি অাপনি কি এবং অাপনার লিখাতে কি অাছে, ।",0,celebrity
"স্যার, এবার স্বাধীনতার পক্ষে মাত্র একটি ভোট দিতে পেরেছি। আমার মা তাও পারেনি দিতে। লাঞ্চ ব্রেক চলছিল তো ১ ঘন্টার জন্য। মা এতক্ষণ দাড়াতে পারেননি। আগামীবার একটু অনুরোধ করলাম, ১০ আংগুল ব্যবহার করে যেন ১০ টা স্বাধীনতার পক্ষে ভোট দিতে পারি এই ব্যবস্থা করেন",0,celebrity
"কে তুমি বৎস, ধরিয়া মৎস, বেচিয়া গঞ্জে, অকুল ও কুঞ্জে, না খাইয়া তাজা, কেনো ভক্ষন করিয়াছো মেয়াদ উত্তীর্ণ গাজা (২)😂😂",0,celebrity
"এই কমেন্ট গুলো পড়তে বসলে তো আমি সব কিছু ভুলে হাসতে হাসতে পাগলী হয়ে যাবো রে,,,,,,,থাক মন খারাপের রাতে এসে পড়ে নিবো আর হিহিহি করো হাসবো!",0,celebrity
আপনার   জন্ম হোউক  যুগে  যুগে  স্যার,0,celebrity
কমেন্ট পড়তে আসছি ...😩,0,celebrity
প্রশ্ন ফাস আটকাতে পারলে ভাল পদ্ধতি.. তবে সব থেকে ভাল হয় স্যাট বা জি আর ঈ টাইপের একটা সিস্টেম ডেভেলপ করতে পারলে..,0,celebrity
"কমেন্ট পড়লাম,অনেক কষ্ট করে বমি চেপে রাখার চেষ্টা করে ব্যর্থ হয়ে হড়হড় করে দিলাম।",0,celebrity
"মন ভাল নেই, তাই কমেন্ট পড়তে আসছি",0,celebrity
এ কুকুর আমার শিক্ষক হতে পারে না! জাতীয় বেইমান।,0,celebrity
অভিজিতকে হত্তার জন্ন মায়াকান্না করতেছস। কিন্ত ইস্লামকে অবমাননা করে যারা মিছিল করেচে তাদের সমমন্দে ত কিচু বলিস নাই।,0,celebrity
"আওয়ামীলিগের দালালদের তালিকা করলে এই লোকটা নিশ্চিত নাম্বার ওয়ানে থাকবে। ওর যে মুক্তিযুদ্ধ নিয়ে এতো চুলকানি কেন সেটাই বুঝিনা। এতোই যখন বুঝেন,তখন যুদ্ধের সময় গর্তে পলায় না থেকে একটা বন্দুক নিয়ে দৌড়াদৌড়ি করতেও তো পারতেন মহা মুক্তিযুদ্ধ বিশেষজ্ঞ???",0,celebrity
"""কোচিং এর ব্যাপারে উন্নত দেশকে উদাহারণ দিতে শুনেছেন"" এই বাক্যটি সম্পূর্ণ সোহাগ ভাইকে উদ্যেশ্য করে লেখা। কারন তিনিই এই উদাহারন টি দিয়েছিলে। এত কিছু লিখেছেন তাহলে সেই টক শো তে সোহাগ ভাইয়ের বাকি যুক্তিগুলো খন্ডন করলেন না কেন?",0,celebrity
পোস্ট না পড়ে কমেন্ট করতেসি.. ...হাহা দিলাম... অনেক শান্তি লাগতেসে....,0,celebrity
উদ্ভট এক উটের পিটে চলেছে ...,0,celebrity
স্যাটেলাইটস আকাশে না দিয়ে পোষ্ট দাতার পাছায় সাপোসিটার হিসাবে ঢুকানো উচিৎ ছিল :(,0,celebrity
আপনি তো জাতীয় দালাল!,0,celebrity
স্যারের পোস্টে মানুষ এত হাসে কেন।,0,celebrity
"এখন যদি স্কুল বা কলেজের কোন ছাত্র বা ছাত্রী  আপনার সামনে এসে বলে আমি ১৮ তে নিরাপদ সড়ক চাই আন্দোলনে যুক্ত ছিলাম,তখন কি তার উপর হরহর করে বমি করবেন!!!????",0,celebrity
"""কোটা সংস্কার আন্দোলন"" কে ""কোটা বিরোধী আন্দোলন "" বলে দিলেন। "" আমি রাজাকার"" ছাত্ররা কেন বলেছে, এটা কি খোঁজ নিয়েছিলেন? এটা যে নিছক প্রতিবাদের ভাষা ছিল আপনি সাহিত্যিক হয়েও তা বুঝলেন না। বুঝতে পারলেন না দেশের ৯৮% লোকের মনের ভাষা। আপনি কিসের.......  সাহিত্যিক।",0,celebrity
"অন্যের ক্ষেত্রে  হিসাবটা খুব সহজে মিলিয়ে দিয়েছেন, কিন্তু বিষয় টা যদি নিজের ক্ষেত্রে হত তখন কি করতেন স্যার???",0,celebrity
প্রত্যেকটা কথা চমৎকার!! অনেক ধন্যবাদ স্যার।,0,celebrity
অতি উৎসাহি মানুষের অবদান আছে কিনা বুঝেন না?,0,celebrity
"কেউ বিভ্রান্ত হবেন্না।ওটা স্যারের ফেক পেইজ,বিজ্ঞানের ভাষায় মরা মানুষ কখনো ফিরে আসতে পারে নাহ।",0,celebrity
"বিদায় নিছেন বালা কথা, শিবিরের বদনামি করে কি সুশীল সমাজে মুরগী কবিরের চেয়ার নিয়ে টানাটানি করার চিন্তা করতেছেন নাকি?",0,celebrity
"আল্লাহ, নবীর শত্রু যারা হয়েযা সাবধান নয়লে জুতার বারি খাবি হয়বি অপমান।  মুসলমানের সাথে বুশ বিয়াদ দবি করেছে  তাইতো ইরাকেতে জুতার বারি খেয়েছে।",0,celebrity
উনি প্রথমেই বলে নিয়েছেন এখন সব কিছু সংবাদপত্রে লেখা যায় না। তাই ধর্ষকদের দেখে হরহর করে বমি করে দেয়ার বদলে হালকা বকে দিয়েছেন। take it positively,0,celebrity
"রাজাকার শব্দ চয়ন যদি এতটাই ভুল করে থাকে ছাত্ররা তাহলে  বিশিস্ট মন্ত্রী মতিয়া চৌধুরি, সাধারণ ছাত্র ছাত্রীকে যখন বললেন ""রাজাকার"", এই নিয়ে কিছু বললেন না কেন? এখানে আপনার দূর্ববলতা স্পস্ট নয় কি??",0,celebrity
"নিজ অতীতে আমার ইসলাম থেকে বেরিয়ে যাওয়া, এবং বর্তমান সময়ের অগণিত তরুণ-যুবাদের ইসলাম থেকে মুখ ফিরিয়ে নেওয়া থেকে আমি স্পষ্টভাবে বলতে পারি, এ ধরনের মতবাদের সমর্থক বই, পত্রিকা, প্রচার মাধ্যম মুসলিম মানসদের জন্য খুবই ভয়ংকর। এর প্রধান কারণ হিসেবে বলব ‘ক্লাস টেন পাশ করা’ ইসলামি শিক্ষা। এ শিক্ষা কেবলই পুঁথিগত। এর কোনো প্রভাব আমাদের ব্যক্তিগত জীবনে পড়ে না। আমাদের বাবা-মা’রাও কথিত প্রগতিবাদ আর পার্থিব উন্নতির প্রতিযোগিতায় দৌড়াতে দৌড়াতে এসব বিষয়ে পাত্তা দেন না। ইসলামিক শূন্য কলসি নিয়ে এসব কিশোরেরা একসময় তরুণ ও যুবক হয়ে ওঠে। পরে সেই কলসিতে যখন এলিয়েন মতবাদ আর দর্শনের ঘোলাজল জমা হতে থাকে তখন সে হয়ে ওঠে ইসলাম-বিদ্বেষী, কিংবা ইসলাম-বিমুখ। সে ভুলে যায় তার স্রষ্টাকে। আপন স্রষ্টাকে ভুলে যাওয়ার চেয়ে বড় বিপর্যয় মানুষের জন্য আর কী হতে পারে? শিশু-কিশোর তো বটেই, আমরা নিজেরাও বই পড়ার বেলায় লেখকের মতাদর্শ ব্যাপারে যেন সজাগ থাকি। কাউকে নবিজির চেয়ে বেশি ভালোবাসি বলে তার সব কথা যেন অন্ধের মতো না গিলি। সবার আগে নিজের ইসলামিক জ্ঞানকে পোক্ত করে কলস ভর্তি রাখি। তা হলে নতুন যেকোনো ভাবাদর্শই আসুক না কেন তা কলস উপচে বাইরে পড়ে যাবে; ভেতরে কুল পাবে না। নীচু আদর্শ নিচেই পড়ে থাকুক।",0,celebrity
এই পোস্টের অপেক্ষায় ফেসবুকিং করতে করতে কাল রাত বারোটার আগেই ঘুমাইছিলাম 😰  সকাল থেকে টিবি দেখিনাই তাই বিনুদুন নিতে আইলাম  😜,0,celebrity
"পায়খানার গু এর ভিতর এ ধ্যান করলো নাকি ৩ দিন,,,,গু খাইতে খাইতে এগুলা মনে ছিলো না,,,গু খেয়ে পেট ভরে গেছে,এখন জ্ঞান ফিরলো😎😎😎😜😜😜👅",0,celebrity
"আমি বন্ধুদের সব সময় বলি,কার মন খারাপ হলে,লাকি,ইমরান,গোলামওলা রনি,জাফর ইকবাল স্যার এদের পোস্ট পড়ার দরকার নাই,শুধু কমেন্ট গুলো দেখুন ১০০% মন ভালো হবেই হবে।  আমি আরো বলে থাকি কারো থেকে লজ্জা পেয়ে মরে যেতে চাইলে, একটু কষ্ট করে মরার আগে জাফর ইকবাল স্যারের পোস্টে করা কমেন্ট গুলো দেখতে, কেমনে লজ্জাকে জয় করতে হয় আমাদের জাফর স্যার সেটা বাস্তবে প্রমান দিতেছে।",0,celebrity
এতো রাতে পিউর বিনোদন উপভোগ করতে আসিলাম,0,celebrity
আপনি একজন লেখক ও বুদ্ধিমান মানুষ হয়ে একটা ধর্মঅবমাননাকারীর হয়ে এইটা কেমন ধরনের কথা বললেন.......,0,celebrity
সাদিকা নাফিস আনুষা  Mrinmoye Mehzabin আপনার কোথায়..? ফুলের তোড়া সাজিয়ে নিয়ে আসেন...!  স্যারকে বরণ করতে হবে তো...! 😞😞😒😒,0,celebrity
"স্যার এই কথা গুলো কি আপনি বলেছিলেন?  "" আমার ধারণা ছিলো- এই প্রজন্ম রাস্তায় নামতে পারে না, তারা শুধু বাসায় বসে ফেসবুকে লাইক দেয়। তোমরা আমাকে ভুল প্রমাণ করেছো। তোমাদের জন্যে গর্বে আমার বুক একহাত পরিমাণ ফুলে গেছে। এখন থেকে তোমরা যখনই দরকার হবে, রাস্তায় নেমে পড়বে """,0,celebrity
আমার শ্রদ্ধাভাজন মানুষ। স্যালুট আপনাদের।,0,celebrity
"কেউ বৃত্তি পাচ্ছে, কেউ না, তখনি ধরেছিলাম,এটা রসিকতা নয়,একটা ধোকা,প্রতারনা ছাড়া আর কিছুই নয়। এই গোল্ডেন জি পি এ আমাদের মতো গরীব অভিবাদকদদের পকেট, শিক্ষক নির্ভর  কোচিং বানিজ‍্য কতৃক  ছিনতাই ও ফতুর করেছে।আপনাদের মতো লোকরাই তা চালু রেখেছে।শিক্ষকদের কোটিপতি বানানোর নির্ভুল পদ্ধতি আবিষ্কার করেছেন। এক একজন শিক্ষকের কোটি টাকার সম্পদ, বাড়ী, বিলাসবহুল গাড়ী,অত‍্যাধুনিক ফ্লাট আরো কত কি। আমরা রীতিমতো জিম্মি। পুলিশের অভিযান আইওয়াশ,পদ্ধতি বহাল রেখে।আরো লিখতে মন চাইছিলো,কিন্তু ঘৃনায় ও থুথু নিক্ষেপ করতে হতে পারে বিধায় লিখলাম না।",0,celebrity
জাফর সাহেব কই আছিলেন এত দিন আপনার গায়বি জানাজা পডা হইছে।,0,celebrity
"স্যাড়ের পোস্টের কমেন্ট গুলা পড়তে আমি এখানে আসি , আর কিছুনা।",0,celebrity
আপনার কমেন্ট পড়ে বিবেকবোধ জাগ্রত করার উচিৎ ছিলো,0,celebrity
বড় যে হইসি এখন বুঝতে পারি।ব্যক্তি জাফর ইকবালকে সম্মান আর দিতে পারি না,0,celebrity
"পৃথিবীতে এক পরিবারে একাধিক সন্তান বুদ্ধি প্রতিবন্ধী হিসেবে জন্ম নেয়া নতুন কিছু নয়।  কিন্তু বিদেশে নামকরা বিশ্ববিদ্যালয়ে উচ্চতর ডিগ্রিধারী তিন তিন জন বুদ্ধি প্রতিবন্ধী সহোদর আমার ক্ষুদ্র জীবনে একটাই দেখলাম। সেটা আপনাদের পরিবার স্যার।  ""দেশ তোমাকে কি দিয়েছে না বলে তুমি দেশ কে কি দিয়েছ? "" এই প্রশ্নো যারা করেন তাদের বলবো  ""যে দেশে গুনীর কদর নেই সেই জ্ঞানীর জন্ম হয় না""   বলে একটা কথা আছে।  Muhammed Zafar Iqbal এর মত এখনো কিছু গুনী বুদ্ধিপ্রতিবন্ধী চাপাতির কোপ খাওয়ার জন্য বিদেশ এর অর্থ সম্মান আর উন্নত জীবন ছেড়ে বাংলাদেশে পড়ে আছেন।  স্যার আপনারা যে দেশের উন্নতির আশা নিয়ে পড়ে আছেন ইতিহাস ঘেঁটে দেখেন  এ দেশের মানুষ তাঁদের জাতীর জনকের বুকেই গুলি চালিয়েছিল।  সে জাতী আপনাদের ছাড় দিবে???  এরা সব অকৃতজ্ঞ।  সুস্থ হয়ে উঠুন।  এটাই একমাত্র কামনা।",0,celebrity
শুধু কমেন্ট Sanzid Saim,0,celebrity
কাহা মুক্তিযুদ্ধ নিয়ে ব্যবসা টা ভালই  চলছে,0,celebrity
"আপনার একজন প্রাক্তন ভক্ত হিসেবে কিছু বলতে চাই -   আপনি দয়া করে দেশ নিয়া লেখা বাদ দিয়া দিন। শেষ বয়সে এসে মানুষ আপনাকে ""আপনি"" থেকে ""তুমি"",  তুমি থেকে ""তুই"" পর্যন্ত এনে অকথ্য ভাষায় গালাগালি দিচ্ছে৷ এটা দেখে আমার কষ্ট লাগে। যত হোক, আপনাকে এককালে পছন্দ করতাম৷    আপনি একজন গ্রামের গুরুত্বহীন মহিলাকে নিয়া ভালো কিছু লিখতে বসেও যে, দলীয় পক্ষপাত থেকে নিজেকে মুক্ত রাখতে পারেন নাই। তা সত্যিই লজ্জাকর৷   আপনি এমনভাবে লিখলেন যেন, গণধর্ষণ হলো ধর্ষণ,  আর নরমাল ধর্ষণ কোন ধর্ষণই না। আপনার কথায় আপনি এ পর্যন্ত যত নারী ধর্ষিত হয়েছে তাদেরকেও অসম্মান করেছেন।  ভাবটা এমন নিলেন আর গণধর্ষণ শুধুমাত্র বিএনপি/জামাতের আমলেই হয়েছে। আর আওয়ামীলীগের আমলে সূবর্ণচরের ঘটনা ছাড়া আর কোন গণধর্ষণই ঘটেনি৷   এমনটা ভাবলে বলতে বাধ্য হচ্ছি, আপনি স্যার অন্ধ হয়ে গিয়েছেন। নয়তো পত্র-পত্রিকা পড়া বাদ দিয়ে দিয়েছেন কিংবা শুধুমাত্র বিটিভি দেখেন।   এইতো কিছুদিন আগেই - টাংগাইলের মধুপুরে রূপাকে বাসে গণধর্ষণ ও হত্যা করলো, মৌলভিবাজারে রাশেদাকে গণধর্ষণ ও হত্যা করলো, রাজবাড়িতে একই মাসের ব্যবধানে দুই নারীকে গণধর্ষণ ও হত্যা করা হয়েছে,  এর মধ্যে আবার একজন প্রতিবন্ধী ছিলো, বরগুনার পাথরঘাটায় এক তরুনীকে গণধর্ষণ ও হত্যার ঘটনায় ৭ ছাত্রলীগ জড়িত (বহিষ্কৃত),  নাটোরের বড়াইগ্রামে গৃহবধূকে গণধর্ষণ ও হত্যা, নরসিংদীতে গণধর্ষণের পর হত্যা (মৃত্যুদণ্ড), গার্মেন্টসকর্মী আসমাকে গণধর্ষণ --- ইত্যাদি গণধর্ষণ ঘটনার বেশিরভাগই শুধুমাত্র গত বছরের।   এবার আসি, আপনার ভাষায় নরমাল গণধর্ষণ!  ২০০৮ সাল থেকে ২০১৬ পর্যন্ত ধর্ষণের সংখ্যা ছিলো মোট - ৪৩০৪ টি! এর মধ্যে ধর্ষণের পর হত্যা হয়েছে ৭৪০ জন। আর এসব রেকর্ড পার করে দিয়েছে ২০১৭-১৮ সাল। এই সরকারের আমলে মোট ধর্ষণের সংখ্যা প্রায় ১০০০০+   এসব আমার কথা না। বিভিন্ন সময়ে টিভি ও নিউজপেপারে আসা সংবাদ!!!   দয়া করে আর দেশ নিয়ে লেইখেন না৷ কষ্ট লাগে৷ একসময়ের সুপারহিরোকে সুপারভিলেনে পরিনত হতে দেখে।  গ্লানি মুক্ত হওয়া এত সহজ নয়৷ গ্লানির বোঝা পাহাড় সমান হয়ে গিয়েছে।",0,celebrity
"স্যার তথ্য এরিয়ে জান কেন??? আমি আপনার লেখাটাকে আর একটু পরিষ্কার করে দিচ্ছি সেইটা হচ্ছে জামায়াত ইসলাম ৯৬ সালে আওয়ামী লীগের সাথে জোট ছিলো সেইটা তোহ একবার বললেন নাহ,আর জামায়াত ইসলামী এর বর্তমান নেতারা কেউ ই তখন রাজাকারের দায়ে জেলে ছিলো নাহ তাদের বিরুদ্ধে তখনকার সময় এর একটা মামলা ও নাই,আর গর্তে কে ছিলো সেইটা আরেকটু মনে করিয়ে দেই যুদ্ধের সময় একজন ২০ বছরের টগবগে যুবক যুদ্ধ না করে কোন গর্তে লুকিয়ে ছিল তা আপনার ভাই হুমায়ূন আহমেদ তার বইতে লেখছেন  আর কারা নির্বাচনে থাকবে না থাকবে এইটা ঠিক করবে জনগণ,আপনি নাহ জনগণ যদি জামায়াত ইসলাম কে না চায় তাহলে ভোট দিবে নাহ আর চাইলে ভোট দিবে আপনার এতো জনপ্রিয়তা নির্বাচন করে জয়ী হয়ে দেখান তোহ দেখি পারেন নাকি?? নিজের জনপ্রিয়তায় তোহ ইউনিয়ন পরিষদের চেয়ারম্যান ও হইতে পারবেন নাহ",0,celebrity
আওয়ামী চামচামি করলে সরকারি চাকরির গুরুত্ব বুঝবেন কি করে?😃,0,celebrity
আপনারে স্যার বলে কোন হা.......ই আপনি আমার চ্যটের বাল😃😃,0,celebrity
"লাইসেন্স বিহীন সরকার, লাইসেন্স বিহীন পুলিশ-বিজিবি। জানতাম তবে দেখাতে পারতাম না। ছাত্ররা দেখিয়ে দিল।  স্যালুট তাদের।",0,celebrity
ভুতের বাচ্চা :-D :-D,0,celebrity
You didn't mention anything about crossfire or similar to those??? You don't have any feelings about those!!!!!!!,0,celebrity
আরে 😱 স্যার আইন্নে না মরি গেসিলেন। আইন্নে মরুইন ন  আইন্না দি জিন্দা। ওমা বেডা এগ্গুন দি ওলৌকিক ভাবি বাচি উডি স্ট্যাটাস ও মারে । কি আইষচোয্য ক্ষেমতা হেতি রোবট ম্যান  হই গেস😱😱😱😱  আই উদ্দাই আর আই ফি (Rip) লেখি লেখি কইতো কইতো  আর ওয়াল ভরি পেলচি😐😤😭,0,celebrity
সুবিধাবাদির মায়রে বাপ 😡,0,celebrity
রিয়েল দে,0,celebrity
"যখন ওই ছেলেগুলোর একটু পাশে দাঁড়ানোর দরকার ছিল তখন হারিকেন দিয়েও খুঁজে পাওয়া গেল না!এখন অনেক দেরি হয় গেছে স্যার!লাখ লাখ জলন্ত আগ্নেয়গিরি,জাতির ভবিষ্যতদের কাছে আপনি আজ নিতান্তই মৃত!!আর আপনার পোস্টটি নিছকই মৃতের প্রলাপ!!!",0,celebrity
"এর উত্তর সহজ, মুতিয়া চৌধুরী কোটা আন্দোলন কারী ছাত্রদের ""রাজাকারের বাচ্চা"" বলে গালি দিছিল, মুক্তিযুদ্ধ নিয়ে যারা ব্যবসা করে তাদের বিষয়ে সচেতন থাকুন।",0,celebrity
"ভাই আমার, পড়ালেখার চাপ থেকে মুক্তির জন্য তোর একটু বিনোদন দরকার। এখানের কমেন্ট সেকশনে ফ্রিতে বিনোদন বন্টন চলছে। ভাবলাম তোর উপকারে আসবে 😌  Abidur Rahman",0,celebrity
আমি মাদারচোদ দেখিনি  তবে জাফর ইকবাল কে দেখেছি।।,0,celebrity
"আপনি ঠিকে বলেছেন,৭১ জারা আমাদের ওপর নিরম্ম হত্ত্যা চালিয়ে ছিল আমরা তাদের পরাজিত করেছিলাম ঠিক কিন্তু ৭৫ এর পর তাদের আবার এদেশে এনে পূণবাসিত করে আমদের সাধিনতার ইতিহাস মুক্তিযুদ্ধ ইত্যাদি ধরর্ম এর মুখো মুখি দার করিয়েছে আর তাদের মত করে একটা প্রজন্ম প্রতিষ্ঠা করে মাদের বিরুদ্ধে দার করিয়েছে আর এরাই এখন মুক্তিযুদ্ধের আপনার আমার সমালাচনা করছে",0,celebrity
"সার, আমার না আপনার পোষ্ট পড়ে বমি বমি লাগছে। উফ কেন পড়লাম? ভাইরা আমাকে একটা আন্টিঃ বিটিক দেন তো যাতে ১০ মিনিট আগের স্মৃতি সব ভুলে যাই।",0,celebrity
"স্যার, আপনি দ্রুত সুস্থ হয়ে উঠুন! দোয়া করি আল্লাহপাক আপনাকে  আরো দীর্ঘ দিন বাঁচিয়ে রাখুন, আমিন!!",0,celebrity
"মুক্তিযুদ্ধের পক্ষের একজন মানুষও কি নাই, যে এই পোষ্টে একটা ভালো কমেন্ট করবে..???  পৃথিবী এত নিষ্ঠুর কেনো....???",0,celebrity
"স্যার আপনি আমার এবং আশা করি এখানের অনেকেরই প্রিয় লেখক। আজ এত শিক্ষার্থীদের ওপর অত্যাচার হচ্ছে,  আপনি কি কিছুই বলবেন না? তাহলে কি ভেবে নেব আপনি আর আমাদের পাশে নেই? আমার প্রিয় লেখক কি এভাবেই মুখ ফিরিয়ে নেবে?",0,celebrity
"আপনি তো দোয়া করছেন তার বাঁচার জন্য। কিন্তু কার কাছে দোয়া করলেন। ওর তো কোন প্রভু নেই। যত্তসব!!!!    আসলে নাস্তিক-ফাস্তিক, ব্লগার বইলা কোন কথা নাই। পরোক্ষভাবে ইসলামের ওপর আঘাত করব এইটাই হইল মূল কথা। আপনিও কিন্তুও এই দলের বাইরে নন।           এখন খুব তো কলম চালাইতেছেন। যখন লতিফ সিদ্দিকি নবিজিকে কটূক্তি করছিল তখন কোথায় ছিলেন?      আর আপনি কিভাবে সিউর হলেন যে ধরমান্ধরাই মারছে। এটা যে আপনাদের কারসাজি কি না, তা কি করে বুঝব!!!!! যুগের সেরা বুদ্ধিজীবী বইলা কথা।",0,celebrity
"আপনি কোন টেনশন নিয়েন না স্যার, আপনার মতো পল্টিবাজদের শহিদুল আলমের মতো টেনেহিঁচড়ে নেওয়ার কোন প্রশ্নই উঠে না। আপনি সহজ-সরল একজন পল্টিবাজ মানুষ। ফেসবুকে আসেন না, ইন্টারনেট ইউজ করেন না, টিভি দেখেন না। তাই বলে কি আপনি উনার মতো এতোটাই বোকা যে, সরকারের সমালোচনা করে কোন ইন্টারভিউ দিবেন! আপনার মতো মহান পল্টিবাজ কি আর একটাও খুজে পাওয়া যাবে এদেশে! অবশ্যই না। কস্মিনকালেও না!",0,celebrity
যাক আজ মুক্তিযুদ্ধের চেতনা নিয়ে কিছু লিখেন নাই 😆,0,celebrity
আসাধারন লিখেছেন sir.,0,celebrity
আজকে কিনে নিয়ে আসলাম ;),0,celebrity
অবশেষ এ জাফর ইকবাল ঘুম  থেকে উঠলো,0,celebrity
স্যার আমি বলার মতো কিছু পাচ্ছি না।। কিন্তু অনেক কিছু বলতে চাই।। আপনাকে আমরা অনেক ভালবাসি।। ♥♥♥♥♥♥♥♥♥♥♥♥,0,celebrity
আমি জাফর ইকবালকে ঘৃনা করি কারন সেনাস্তিক,0,celebrity
"১৯৭১ আর ২০১৮ কত মিল। সেইম ঘটনাই ঘটল। সেই নাপিতের দোকান। শুধু উত্তরটা ভিন্ন। আমি ""ছাত্রলীগ"" করি। কি অস্মভব মিল।",0,celebrity
মীর জাফর ইকবাল!!,0,celebrity
কমেন্টযোদ্ধাদের বলছি আপনারা ছোট করে কমেন্ট করবেন যাতে সবারটা পড়তে পারি 😁,0,celebrity
আবারো PSC Exam এর পরীক্ষার প্রশ্ন আবার ফাস হচ্ছে|এটাই কি শিক্ষা ব্যবস্থা|,0,celebrity
আজ জুম্মা মোবারক! সারাদিন ফ্রি আছি।দুমাইয়া কমেন্ট পড়বো!,0,celebrity
আপনার ডিকবাজী কীটকেও হার মানাবে।,0,celebrity
"আজকে জীববিজ্ঞান ক্লাসে স্যার বললেন,"" এই টপিকটা ইন্টারেস্টিং,  কিন্তু আমি এইটা এখানে পড়াবো না। এইটা আমি পড়াবো #প্রাইভেটে  ।"" 🤘🤘",0,celebrity
জয় বাংলা,0,celebrity
বর্তমানে আমাদের দেশে দালালি ব্যাবসা সবচেয়ে ভালো ব্যাবসা...!!!! চালিয়ে যান..আপনি পারবেন...?????,0,celebrity
নাস্তিক নাস্তিক নাস্তিক,0,celebrity
কাকু আপনাকে সিফাত কাকু নিমন্ত্রণ জানিয়েছেন।।।  কয়েকটা বেত নিয়ে যেতে বলেছেন।।,0,celebrity
"নতুন বছর আমাদেরকে চরম দুঃসময়ে গর্তে লুকিয়ে না থেকে লড়াইয়ে ঝাপিয়ে পড়ার প্রেরণা যোগাক। সেই সাথে, শত অন্যায় চোখে দেখেও সুবিধাবাদী পজিশনে থেকে দালালী না করে অন্যায়ের বিরুদ্ধে সোচ্চার হওয়ার প্রেরণা যোগাক।",0,celebrity
"স্যার, এতই যদি ঘেন্না হয় তবে বমি করতে গলায় আঙুল দিতে হবে কেন!? কোষ্ঠকাঠিন্য শুনেছি, বমিকাঠিন্য একান্ত আপনার বেলায়ই সম্ভব।",0,celebrity
"আপনার চোখে এটা ধরছে না যে বালুর ট্রাক দিয়ে অবরুদ্ধ রেখে সমাবেশেরর অনুমতি না দিয়ে পুলিশি প্রহরায় সরকার সমাবেশ করছে। হরতাল অবরোধই কেবল চোখে ধরছে তাই না!!! ভাল স্যার,আপনার লেখা পড়লে একসময় আবেগে চোখে জল নেমে আসত আর আজকাল পড়ে মনে হয় কারো বলে দেয়া কথাটাই আপনি পুতুলের মত বলছেন। আপনার ভাইয়ের কাছ থেকে নৈতিকতাটা ঠিকঠাক শেখা দরকার ছিল আপনার।",0,celebrity
সহমত স্যার..,0,celebrity
কমেন্ট পড়ে মজা নিতে আসছি..,0,celebrity
"এতু সুন্দুর পুষ্ট করার জুন্যু আপনাকে দেয়া হবে কেয়া কসমেটিক্স এর পক্ষ থকে মহা মুল্যবান বই, এবং পরিবেশ বান্ধবগাছ...😂😂 ক্ষ্যাপা",0,celebrity
গ্যাবাডিং প্যান্ট কিনুন সবচেয়ে কম দামে Price BDT 550  www.facebook.com/Pick.Purchase.BD/posts/2553548811322100,0,celebrity
"পলিটিক্স থেকে দূরে থাকুন.. আপনি বুঝতেও পারবেন না, আপনার কেউ না কেউ ইউজ করছে। দিন শেষে দোষ ঘাড়ে পড়বে মৌলবাদীদের।",0,celebrity
"৯৯.৯% কমেন্ট দ্বিমত শোষণকারী।  এদের মধ্যে আবার ২০-৩০% নিচু মনমানসিকতার,  যারা গালাগালি করতেছে।  তবে বিনয়ের সাথে বলছি স্যার, অনেক তথ্যের গ্যাপ রয়ে গেছে।",0,celebrity
"ফিরে আসুন স্যার, আমাদের পথের দিশারী এভাবে চলে যেতে পারে। আপনার দৃঢ়তাই আমাদের অনুপ্রেরণা! #GetWellSoonSir. #WeAreZafarIqbal.",0,celebrity
স্যার চলেন নামাজ পড়ে আসি!  😂,0,celebrity
সাস্ট এ কত জন পরীক্ষা দিতে পারে,0,celebrity
"অনেক হলো। গোটা দেশ তোমাদের সাথে সংহতি জানিয়েছে, এবারে ঘরে ফেরার পালা। তোমাদের চাওয়াগুলো পূর্ন হয়েছে। নিহত সহপাঠী দিয়া আর করিমের পরিবারও তোমাদের ঘরে ফিরে যেতে আহবান জানিয়েছে। নিশ্চয়ই রবিবার থেকে আবারো তোমাদের কলরবে মুখরিত হবে স্কুল।    আন্দোলনটা নিজের ঘরে কর। তাহলেই দেখবে সব ঠিক হয়ে যাবে। বড় ভাইবোন হয়েছো বলে ছোট ভাইবোন যেন ভালবাসা হতে বঞ্চিত না হয়,  বোন হয়ে জন্মানোর কারণে শারীরিক,  মানসিক, সামাজিক, অর্থনৈতিক ও পারিবারিক সহিংসতা যেন না হয়। গারিতে যখন বয়োজ্যেষ্ঠ দেখবে নিজে উটে বসতে দিবে, মুরুব্বীদের সামনে সিগারেট খেয়ে আদবের বরখেলাপ করবে না। কাল সকালে স্কুলে যাওয়ার আগে মাকে বলবে অযথা চুলা জ্বালিয়ে না রাখতে, গ্যাসের অপচয় কমবে।  বাবাকে বলবে অফিসে ঘুষ না খেতে, কাজে ফাকি না দিতে।  ভাইয়াকে বলবে রং সাইডে গাড়ি না চালাতে, ট্রাফিক আইন মানতে, রাস্তায় এম্বুলেন্স, ফায়ার সার্ভিসের গাড়িকে সাইড দিতে বোনকে বলবে ফুট ওভারব্রীজ দিয়ে রাস্তা পার হতে, আইল্যান্ড দিয়ে হাটতে। এভাবে নিজের ঘর আর নিজেকে ঠিক কর। দেখবে দেশটা ৮০% ঠিক হয়ে যাবে।",0,celebrity
Ziaur Rahman Shaheb er chele akta beyadob. Alem er ghore jalem hoice.........,0,celebrity
স্যার কতদিন টিক'টক করতে পারেন এতে মনটাও হাল্কা হবে আবার জাতি কিছু বিনোদনও পাবে।,0,celebrity
"আজকের দিনে এই সময়ে যারা শুধুমাত্র একটি সরকারী চাকরী পাওয়ার জন্য ( যদিও ৯৯ % ই এই সোনার হরিণটা পাবে না কিন্তু আন্দলনে গেছে পাওয়ার উদ্দেশ্যে, তাদের অনেকের ধারণ কোটা উঠিয়ে দিলেই তারা অটো চাকরিটা পেয়ে যাবে।তাদের বলি সরকারী চাকরি মাগনা আহে না, জীবন ত্যানা - ত্যানা করে ফেলতে হয়, সো রাস্তা এবং বিকল্প রাস্তা একটাই সেটা হল পড়াশুনা, আরেকটা কথা যেই ১% সারাজীবন ৪৪% সরকারী চাকরি, ক্যাডার হয়ে আসছে তারা এই ৪৪% এ ই আজীবন সরকারী চাকরি, ক্যাডার হবে আর বাকি ৯৯ % আগের অবস্থায়ই থেকে যাবে গ্যারান্টি দিচ্ছি, বিফলে পয়সা ফেরত  ) জাতীর সূর্যসন্তান, জাফর ইকবাল স্যারদের মত মানুষদের অবমাননা, অবজ্ঞা, অকথ্য ভাষায় গালি-গালাজ এবং তাদের বিরুদ্ধে যেতে পারেন খবর নিয়ে দেখেন তাদের পূর্বপুরুষগনই ৭১ এ তাদের ক্ষুদ্র সার্থ আর জানমালের জন্য নিজেদের বিক্রি করেছিল এবং বেচে দিয়েছিল দেশ মাতৃকাকে হায়না - পশুদের হাতে। সবচেয়ে বড় কথা প্রধানমন্ত্রী, জনপ্রশাসন সচিব এবং গুনিজন খুব ভাল করেই জানেন কোটাধারীদের মধ্যে মেধাবীরাই জায়গা পাচ্ছে বাকিরা না।                        ----------সত্য উদঘাটনে সত্যান্বেষী--------                                       "" সত্য প্রতিপাদিত""",0,celebrity
লেইট আপলোড নাকি স্যার?,0,celebrity
"স্যার আপনি ভাল থাকবেন। এ লজ্জা আমাদের, আপনার নয়।",0,celebrity
এতদিন কান চোখ কই ছিল? 😍,0,celebrity
"আগামী দুইযুগের মধ্যেই শুধু দেশের ছেলেমেয়েরা নয়, বিদেশী ছেলেমেয়েরাও এদেশের দিকে ছুটবে! ❤",0,celebrity
". কিন্তু দেখেন Mainul Islam  এর comment ?? :D ............. তাঁর অবস্থান পরিস্কার করার জন্য, ফেসবুকে প্রোপাগান্ডা চালাতে হবে ----------- আমার মনে হয় না স্যার এতোটা ক্ষুদ্র।",0,celebrity
এতো বড়ো পোস্ট পড়বো কখন...? ................তাই কমেন্ট গুলো পড়ছি,0,celebrity
দোষ টা আসলে স্যারের না😛😛😛 একথা প্রমাণিত সত্য যে পলাশী যুদ্ধের পর যাদের নাম জাফর হয়েছে তাদের মধ্যেই সংক্রমিত হয়েছে গাদ্দারির বীজ।ক্যান যে উনার নাম মীর জাফর রাখল😒😒 ধুর ভাল্লাগেনা,0,celebrity
আর কতবার ক্ষমা করবো আপনাকে?,0,celebrity
তুমি বেচে আছো বন্ধু 🙄 আমি তো জানাযা পড়ে চুদ্দু কেজি জিলাপি কিনে মদে চুবাচ্ছি আর খাচ্ছি চুবাচ্ছি আর খাচ্ছি 🍷 তোমার জীবিত থাকার কথা শুনে তো ভয়ে বমিই করে দিছি😥 এখন আমার চুদ্দু কেজি জিলাপির আর বাড়া লিটার মদের কি হবে বন্ধু🤔,0,celebrity
আহহারে গর্ত যুদ্ধা,0,celebrity
সকাল সকাল কমেন্ট গুলা পড়ে অনেক হাসতেছি,0,celebrity
"""এখন যে রকম ছাত্রলীগের দৌরাত্ম্যে সবার জীবন দুর্বিসহ তখন ছাত্রদল-শিবিরের সেই রকম দৌরাত্ম্য।""  what was that!👀👀",0,celebrity
দুরররর... হারামজাদা দালাল,0,celebrity
আপনার জন্য হৃদয়ের অকৃত্রিম ভালোবাসা রইল স্যার। যদি একটা নির্দিষ্ট প্রজাতির গায়ে আপনার অন্যান্য লেখার মতই এই লেখাটিও কাটা গায়ে নুনের ছিটার মত লাগবে। তাঁরা আপনার ঘাড়ে কোপ না দিতে পারার ক্ষোভ এই স্ট্যাটাসের হাহা রিয়েক্ট দিয়ে এবং কমেন্টে বংশের পরিচয় দিয়ে মিটিয়ে নিতে চেষ্টা করবে।,0,celebrity
জাফর ইকবাল স্যার যখন নিরাপদ সড়ক নিয়ে কাজ করেছেন তখন অামদের বর্তমার প্রজন্ম হয়ত অনেকেই অ অা শিখা হয় নাই। তার সড়ক নিয়ে ১ম কলাম বের হয় ১৯৯৯ সালে ভোরের কাগজে।,0,celebrity
পৃথিবী বানান ঠিক কর চাটা !!!,0,celebrity
"স্যার কে দয়াকরে ভদ্র ভাষায় গালাগালি করেন,বানান টা যাতে ঠিক হয়, আমরা যারা কমেন্ট পড়তে এসেছি সুষ্ঠ ভাবে পড়তে পারি লাইক কমেন্ট করে পাশে আছে ধন্যবাদ ❤",0,celebrity
এতো একটা মুনাফেকের চরিএ। ঘিণা করি,0,celebrity
আমার প্রশ্ন স্যার কেন পাঠকদের কাছে ক্ষমা চাইলেন? কোন দোষে? কি সমস্যা! আজব তো!!,0,celebrity
এই গরিবেরা কমেন্ট পড়তে এসেছি বানান ভুল করিস না,0,celebrity
"এ জন্যই কবি কাজী নজরুল ইসলাম তরুনের জয়গান করেছেন, তবে জনাব একটি ? বোদক রয়েই গেল  আমাদের রক্ষণাবেক্ষণ কাজের জন্য,",0,celebrity
স্যার ! আপনার প্রতিটি  লেখা পড়ে আমি মুগ্ধ হই । জীবনে ভুল(!) করে কোন কিছু করে ফেলার পর কিভাবে তা ১৮০ ডিগ্রিতে ঘুরাতে হয় তা শিখে ফেললাম।  আগের অবস্থান থেক সরে আসার ব্যাখ্যাটা অনেক সুন্দর করে উপস্থাপন করে অনেক কিছুই শিখালেন যা ভবিষ্যতে এদেশে  বেঁচে থাকার কৌশল হিসেবে আমাদের কাজে লাগবে।আরও কিছু টিপস তরুন প্রজন্মকে শিখানোর জন্য আল্লাহ আপনার হায়াত দারাজ করুক   ।,0,celebrity
জাতিকে আপনার কমেন্ট বক্সে হরহর করে বমি করার সুযোগ করে দেওয়ার জন্য আপনাকে ধন্যবাদ 😊,0,celebrity
য়ামাগো ঝাপড় সাপ অনেকদিন পরে লিখলো তাই #কমেন্ট দেখতে য়াসীলাম এসেই য়ামী #সীহোরিত,0,celebrity
স্যার আপনি সত্যি বাইচা আছেন এইটা কোন গুজব না তোহ।,0,celebrity
স্যারের ইমেইল কি পাওয়া যাবে?,0,celebrity
অসাধারন একটা লেখার জন্য ধন্যবাদ।,0,celebrity
আমাদের কি হবেস্যার? ...,0,celebrity
পোস্টের চেয়ে কমেন্ট গুলা বেশি জোশ........😂😂,0,celebrity
স্যার আপনার গাড়ির লাইসেন্স আছে তো...?😂,0,celebrity
"স্যার, আপনার জন্য দোয়া রইলো, দোয়া রইলো ঐ চাঁদটা ছুতে পারবেন ভালোবাসার চোখ দিয়। আমাদের মাঝে বেঁচে থাকবেন, ঐ নর্দমার কীট রা আপনার কিছুই করতে পারবে না।  সত্যিই একটা বার ভাবেন আর ঐ চাঁদমাখা মূখগুলোর মাঝে আপনি আছেন। ঐ চাঁদমাখা একটা মূখ কখনো ধূসর করবেন না, নইলে মানুষরুপী পশু গুলো আরোও গর্জে উঠবে। সুস্থ্য হবেন তাড়াড়াড়ি আর আমাদের মাঝে একটাই চাঁদ আলোকিত করুক এ প্রার্থনা সৃষ্টিকর্তার কাছে করি।",0,celebrity
তারপরেও আপনি নাস্তিক। 😞,0,celebrity
"অসংখ্য শিশুর শৈশব, কৈশোর কে নতুন রূপদানকারী, হাজারো তরুনের স্বপ্নদ্রষ্টা  মহান মানুষটি আমাদের ভিতর বেঁচে থাকবেন যুগ থেকে যুগান্তর পর্যন্ত। শুভ  জন্মদিন আমার প্রিয় লেখক ড. মুহম্মদ জাফর ইকবাল স্যার....",0,celebrity
ভালো লাগলো কথাগুলো :),0,celebrity
স্যার আপনি ফালতু,0,celebrity
নাস্তিকরা আর কিই বলবে!,0,celebrity
"স্যার, ভাবার্থ বুঝার জন্যে অামি অাপনার স্ট্যাটাসের কমেন্ট গুলা পড়ি।তাই বলে স্ট্যাটাস পড়ার প্রয়োজন হয় না....",0,celebrity
"স্যার, এই আন্দোলনকারীদের রাজাকার বানানো যায় না?",0,celebrity
কমেন্ট করার জন্য নয়! বরং কমেন্ট পড়ার জন্য আসলাম..😆😂,0,celebrity
আপনার কোন পোস্টে হরহর করে বমি করিনি। আজ বমি করলাম এক ডাস্টবিন সমান 😡😡😡,0,celebrity
"আপনি নাম্বার ওয়ান দালাল। এবং প্রাণী হিসাবে একটি নিচুমানের কীট। কিছু মনে করবেন না স্যার, এই কথাগুলাই আপনার প্রাপ্য।",0,celebrity
আপনি কঠিন পল্টিবাজ,0,celebrity
"#ধর্ষনের_সাজাঃ- 👉আমেরিকাঃ-ধর্ষিতার বয়স ও ধর্ষনের মাত্রা দেখে ৩০বছর পর্যন্ত কারাদন্ড। 👉রাশিয়াঃ-২০বছর সশ্রম কারাদন্ড। 👉চীনঃ-কোনো ট্রায়াল নেই,মেডিকেল পরীক্ষার পর মৃত্যুদন্ড। 👉পোল্যান্ডঃ-হিংস্র বন্য শুয়োরের খাঁচায় ফেলে মৃত্যুদন্ড। 👉মধ্যপ্রাচ্য আরব দুনিয়াঃ-শেষ নিঃশ্বাস ত্যাগ করা পর্যন্ত পাথর ছুড়ে মৃত্যু,ফাঁসি,যৌবন নাশক ইনজেকশন পুশ করে কারাদন্ড। 👉দক্ষিন আফ্রিকাঃ-২০বছরের কারাদন্ড। 👉মঙ্গোলিয়াঃ-ধর্ষিতার পরিবারের হাত দিয়ে মৃত্যুদন্ড দিয়ে প্রতিশোধ পুরণ। 👉 নেদারল্যান্ডঃ-নির্যাতনের আআলোকে ভিন্ন ভিন্ন সাজা। 👉আফগানিস্তানঃ-৪দিনের ভিতর গুলি করে হত্যা। 👉পাকিস্তান ও মালয়শিয়াঃ-মৃত্যুদন্ড। 👉বাংলাদেশেঃ-প্রতিবাদ,ধর্না,তদন্ত,সমঝোতার চেষ্টা, ঘুষ দেওয়া,অপরাধী প্রভাবশালীদের লোক বলে মামলা তুলে নেওয়ার হুমকি,মেয়েটির চরিত্র নিয়ে গবেষণা, মেয়েটা পর্দা করতো না বলে বদনাম করা,সংবাদমাধ্যম ও টকশোতে আলোচনার আসর,রাজনীতিকরন,জাতি ও ধর্মগত বিভাজন তৈর এবং,প্রভাবশালীদের সহায়তায় উচ্চ আদালত থেকে জামিন।।",0,celebrity
আপনি মানুষ না ড্রাগন?  সাইন্স ফিকশন লিখছেন এত এত৷ আর ফেসবুক লাইভ বোঝেন না?,0,celebrity
"JSC তে মাত্র একটা সাবজেক্ট এ মিস করায় আমার GPA-5 হয়নি।অথচ আমি আমার জেলায় সবচেয়ে স্বনামধন্য স্কুলের ছাত্রী এবং আমার রোল নাম্বার ২০।class er প্রায় সবাই A+ পেয়েছে, কেবল আমি ছাড়া। আমার যেসব বন্ধুরা আমার তুলনায় অনেক পিছিয়ে ছিল তারা পর্যন্ত A+পেয়েছে  অথচ আমি মিস করেছি, তাও আবার ইসলাম শিক্ষায়! Class 9 এ ওঠার পর আমি সম্পূর্ণ আশাহীন হয়ে পরেছিলাম আর নিজের ওপর confidence হারিয়ে ফেলেছিলাম। এতদিন আমার মনে হত কেবল আমাকেই কেন এত কষ্টকর পরিস্থিতির সম্মুখীন হতে হল? এখন প্রিয়াঙ্কার ঘটনা পড়ে মনে হচ্ছে হয়তোবা আমিই একমাত্র না।",0,celebrity
"গর্তেলুকয়ে থাকার মুখে আবার মুক্তিযুদ্ধের চেতনা, এই চেতনা কোথায় ছিল!!  গর্তের ভিতরে",0,celebrity
প্রথমে ভালছিলাম বালের পোষ্ট  পরে দেখি আসলেই বালের পোষ্ট!😂,0,celebrity
কুম্ভকর্ণের ঘুম ভেংছে ঘুম টা কে ভাংগিয়েছে এইটা ওপেন সিক্রেট  অন্য ভাড় গুলো আগেয় এসেছিলো  শুধু আপনার অপেক্ষায় ছিলাম ষার...,0,celebrity
নির্লজ্জ দালাল,0,celebrity
"যখন প্রথম একটা পোস্ট দেখলাম যে আপনাকে আক্রমণ করা হয়েছে চোখটা সাথে সাথে ঝাপসা হয়ে গিয়েছিল, বুকে যে মোচড় টা লাগলো তাতে বুঝলাম আপনাকে কতটা ভালবাসি..",0,celebrity
স্যার চোখে পানি এলো কেন বলতে পারবেন?? ভাল হয়ে উঠুন।।,0,celebrity
Zafar sir apni karkasi doae korcilan Allha naki bogobanarkaca karon sa to nastik cilo.,0,celebrity
গল্পের নামঃ বাবা লেখকঃ রায়হান পারভেজ। লিংকঃ https://m.facebook.com/story.php?story_fbid=962813160536430&id=747873045363777,0,celebrity
"স্যার, আপনি তাড়াতাড়ি সুস্থ্য হয়ে উঠুন। আমরা আপনাকে ভালবাসি, আমাদের সংখ্যাটাও নেহাৎ কম নয়।   ওরা তো জানে না,  ভালোবাসা ভালোবাসাকে বাঁচিয়ে রাখে। ঘৃণা শুধু পুড়িয়ে দেয়, ছারখার করে, ধ্বংস করে। ওরা যদি সাময়িক কিছুতে জিতেও যায়, এ চিরকালের নয় কখনো। সত্য, সুন্দর, মানবতার জয় হবেই হবে।",0,celebrity
"স্যার আপনি অনন্তকাল বেঁচে থাকুন,এই প্রার্থনা করি",0,celebrity
"একটা A+ ই যেখানে সবকিছু সেখানে এটা সম্ভব না!  আমার এক বন্ধুর কথাই ধরুন, একবার শোনা গেলো বিশ্ববিদ্যালয় uগুলোতে ২য় বার পরীক্ষা দেয়া যাবে না। সে বলল,  তাতে কি প্রাইভেটে তো আর ১ম - ২য় নাই!    এটাই চিন্তা ধারা :) সেও কিন্তু A+ পাইছিলো..... :)",0,celebrity
সুর পাল্টিয়েছে,0,celebrity
"জাফর ভাই চটি আর কাল্পনিক বই,, অন্য দেশের মুভির নকল ভার্সন বই লেখে, দালালি করে নামে মাত্র নাম করা যায় বাট কখনো মানুষের মনে জায়গা হয় না,,,যাই হোক শিক্ষাবিদ এর তকমা ছেড়ে,, কোনো রাজনৈতিক দলে নাম লিখান,,আর এই জন্য আপনার জন্য আমার সুচিন্তিত মতামতের দল হচ্ছে""""বাংলাদেশ সুবিধাবাদী দল(বাসুদ)!!!!",0,celebrity
"আমি শুধু কমেন্টস পড়তে আসলাম, দয়া করে ঠিক ঠাক মত বানান লিখবেন সবাই",0,celebrity
বিজ্ঞান কল্পকাহিনি লেখক আর কিছু না পেয়ে এখন নোংরা রাজনীতির হাগু চাটছে  এ দেখে হর হর করে বমি করে দিতে ইচ্ছে করে,0,celebrity
"নিরব কেন এই দেশের বুদ্ধিজীবী /সুশীল সমাজের মানুষরা??কোথাই আছে জাফর ইকবাল স্যার, আনিসুল হক স্যার, তারা কি কিছু দেখে নি নাকি কিছু শুনে নি।কিছু দিন আগে যখন জাফর ইকবাল স্যারের উপর হামলা হল তখন ছাত্র রা সবার আগে এগিয়ে গিয়েছিল, প্রতিবাদ করেছিল কিন্তু যখন ছাত্র দের উপর হামলা হল, গুলি চালানো হল তখন তো তিনি প্রতিবাদ করেন নি।কোথাই গেল তাদের প্রতিবাদী ভাষা।নাকি ৭১ এর পরে এই দেশে কোন বুদ্ধিজীবী তৈরি হয় নি।হয়ত আগে তাদের কে যে সম্মান দিয়েছিলাম  তার যোগ্যতা তাদের নাই",0,celebrity
"কিছু ডেট লিখছি দেখেন ত মিল পান কিনা??  May 11(শুক্রবার):আমি রাজাকার: একটি আলোকচিত্র may 25(শুক্রবার):টুকিটাকি ভাবনা June 08(শুক্রবার):সমন্বিত ভর্তি পরীক্ষা june 22(শুক্রবার):আমাদের ক্ষমতা আমাদের অধিকার july 07(শুক্রবার) :ওয়ার্ল্ড কাপ july 20(শুক্রবার):আমার গণিত অলিম্পিয়াড august 03(শুক্রবার):মৃত্যুর এই উপত্যকা  গত মে মাস থেকে জাফর ইকবার স্যার এর লেখা প্রকাশের তারিখ।কি অদ্ভত মিল তাই না??মিলের কারন হলো তিনি লেখেন একটা পত্রিকায়।শুক্রবার সংখ্যা এর জন্য তাও মাসে দুই বার।তিনি আমাদের মত কেউ না যে মন যা চাইল সাথে সাথে পোষ্ট করলাম ফেসবুকে।এটাও জানার বিষয় তার কোন ফেবু আইডি ও নাই।😅😅একটা পেজ আছে ভেরিফায়েড যা আমাদের ডিপার্টমেন্ট এর বড় ভাইয়ে রা চালায়। বাংলাদেশ International Math Olympiad এ সোনা জিতল 14 july ।যেই লোকটা ম্যাথ অলিম্পিয়াড শুরু করল বাংলাদেশে অথচ তার প্রতিক্রিয়া আসল ০৬ দিন পরে কারন লেখাটা আগেই লিখছিলেন বাট সেটা পত্রিকায় টাইমলি পাব্লিশ হতে ০৬ দিন লেগে যায়।এদিকে আমরা সবাই ""ইসটেটাস"" দিয়ে ভরে ফেলছিলাম।মনে আছে??😂😂  তিনি ""মৃত্যুর এই উপত্যকা"" লেখা টা লিখেছিলেম ০১ আগস্ট (ভেরিফায়েড পেজ এর নিচে ডেট দেওয়া) এবং পাব্লিশ ডেট ০৩ আগস্ট ১২ঃ০০ (পত্রিকাটির অনলাইন সংস্করন বের হয়ার সাথে সাথে)  এখন যারা গায়েবি জানাজা পড়লেন কিংবা পোষ্ট দেখলেই খালি পেটের ভিতরে মোচর মেরে বমি করতে মনে চায় তাদের উদ্দেশ্যে বলছি্‌,........."" তুমি কি চুলডা ছিড়া ফালাইছ??""🤔🤔",0,celebrity
"আমাদের উচ্চ পদস্থ কর্তারা যতই মুখে বলুক,  কোচিং ব্যবসা তারা বন্ধ করতে চায়!!!  এই PSC দেবার নাম করে, তারাই কোচিং ব্যবসাকে জাগিয়ে তুলছে!!!!!  আগে শিক্ষার্থীরা মেট্রিক ও ইন্টার মেডিয়েটে কোচিং করতো!!!  কিন্তু বর্তমানে ৫ম শ্রেণি থেকেই কোচিং করা শুরু করছে!!!!  পরীক্ষার আগে তিন মাস ধরে মডেল টেস্ট দিচ্ছে, এইসব কোমলমতি শিক্ষার্থীরা।  রীতিমতো এই বয়সেই তাদের কে যুদ্ধের ময়দানে নামিয়ে দেয়া হচ্ছে!!!!!!!!  অথচ কয়েক বছর আগেও পরিস্থিতি আরো ভালো ছিলো।  কোন কলেজ, ভার্সিটি এই certificate এর মুল্য দেয় না,  তবুও কেন এইসব বাচ্চার অভিভাবকরা, বাচ্চাদের নিয়ে এই পরীক্ষার জন্য যুদ্ধ করছেন!!!  তা আমার বোধগম্য নয়!!!!  আর উপরস্থ কর্তারাও বা কেন কোচিং ব্যবসাকে জাগিয়ে তোলবার জন্য সুযোগ দিচ্ছে!!! সেটাও আমি বুঝতে পারছি নাহ!!!!",0,celebrity
"আল্লাহ আমাদের সকলের কর্ম বিচার করবেনে এর হাত থেকে কউ  রেহাই পাবে না। পরকালে সবাই যাব। ছোট এই পৃথিবীতে যে সময় পাওয়া যায় তা খুব বেশি নয়। ধর্ম নিয়ে বাড়াবাড়ি করা ঠিক নয়। অতএব শান্তিতে থাকা, নিরাপদে বসবাস করার জন্য যা দরকার তা হলো একে অপরকে সহযোাগিতা করা।সকলেই একদিন তার ভুল বুঝতে পারবেন। ভুল বুঝতে না পারলে আপনার আমার কোন ক্ষতি নেই। কিন্তু এমন কিছু করা উচিত নয় যার জন্য বিতর্কীত হতে হবে।এখানে এবং পরকালে ।",0,celebrity
"স্যার প্রথম আলোর দেয়া ডোনেশান থেকে কত টাকা মেরে দিয়েছিলেন??আমারতো মনে হচ্ছে, ভাগ্যিস!! প্রথম আলো টাকাটা দিয়েছিল,নয়তো প্রথম আলোকেও বমি করে দিতেন।",0,celebrity
"হু ছ্যার, পাকিস্তান নোবেল পুরষ্কার দেয় 😂😂 এই প্রথম জানতে পারলাম! আপনার মত তেলবাজ বাংলাদেশে জন্মেছে বলে টিকে আছেন গো ছ্যার, অন্য দেশে হইলে বা* গজানোর আগেই আপনাকে পাগলাগারদে রেখে দিতো। আপনি উচ্চশিক্ষিত হতে পারেন, তবে সেটা সঠিক শিক্ষা নয়। তেলবাজরা যতই উচ্চশিক্ষিত হোক, এরা দেশ ও সমাজের জন্য সবসময়ই মারাত্মক ক্ষতিকর 😊",0,celebrity
"স্ট্যাটাস এর পিছনের কথা, ভাবছিলাম পোলাপাইন দুইদিনে পুলিশের তাড়া খেয়ে ঘরে ঢুকবে.. তখন পোলাপাইনরে ঘরে ঢুকার আহবান জানামু। এখন দেখি আন্দোলন জমে উঠছে, স্রোতে গা ভাসিয়ে সাপোর্ট করা উচিত, তাও চুপ করে ছিলাম, নয়তো আবার সরকারি চাপে পড়তে হবে। কিন্তু এই ত্যাদড় পোলাপাইন গুলা আমার গায়েবানা জানাযা করায়া ছাড়লো.. এখন তো সাপোর্ট করতেই হয়... নইলে আবার কখন ধইরা কবর দিয়া দেয়।",0,celebrity
"বেল্ট, জুতা, মোবাইল, মানিব্যাগ, ঘড়ি, হাতের ব্যাইচ, হেডফোন কিংবা মাথার ক্যাপ সবকিছুই চ্যাক হয়!   তাও আমাদের মধ্যপ্রাচ্যের দুবাই, কাতারের এয়ারপোর্টেই!   এইগুলা এতো আহামরি কিছুনা, য",0,celebrity
দালাল,0,celebrity
yesh very very problem becouse 1ti quetion jokhon out hoy  tokhon result valo korar asha nea movment thake quetion out hole common quetionti Uncommon hoye jay a jonno queation out howa moteo valo na.,0,celebrity
মুক্তিযুদ্ধে না গিয়ে গর্তে লুকিয়ে ছিলেন কেন?আপনার মত দলবাজদের সবাই চিনে ফেলেছে,0,celebrity
সুস্হ হয়ে উঠুন স্যার ♥,0,celebrity
আপনার মতো ষাঁড়দের এখন ভারতে খুব প্রয়জন কারন সেখানে এখন সমকামিতা বৈধ  আপনার মতো অপদার্থ কোন নাস্তিকের জন্য হয়তো কোন সমকামি অপেক্ষা করছে আর দেরি না করে আপনাদের ভারত মাতার কাছে ফিরে যান আর অবলিলায় গো মূত্র পান করুন,0,celebrity
স্ট্যাটাস কার বালে পড়ে 😁 আইলাম কমেন্ট পড়তে।,0,celebrity
"জারজেরা স্যারেরে ট্রল করতেছে এখানে,গালি দিচ্ছে, তাদের জন্ম পরিচয় দিচ্ছে গর্বের সহিত 😂😂  এমন জারজ দেখিনিতো কোথায় 😎",0,celebrity
"আহা! এজানি শান্তির দেবদুত হিসেবে আবির্ভুত হয়েছে। এতই যদি শান্তিবাদী হয়ে থাকেন তাহলে জনগনের ভোটাধিকার,সুসাশন এগুলির জন্য সোচ্চার হোন। তাহলে বুঝবো আপনি সুশিল না কুশিল!",0,celebrity
"আমারা তো গিনিপিক,আমাদের উপর পরিক্ষার উপর পরিক্ষা হএ",0,celebrity
সবাই হড়হড় করে বমি করে দিচ্চে মাইরি।  স্যার ১০ টাকার টিস্যু আইনা দিই?? আপনার গায়ে যাতে না পড়ে 💔💔,0,celebrity
তোফ!!!!! অসভ্য কোথাকার!!!!! বেত্তমিজ!!!! বেহায়া!!!! লাজলজ্জার মাথা খাইছস?,0,celebrity
এই সব কুশিক্ষাবিদ ষ্রারগন কথা বলার সময় ৯০% ই ইংরেজিতে কথা বলেন। এমন কি তাদের পরিবারে লোকদের সাথেও বেশির ভাগ সময় ইংরেজিতে কথা বলেন।   আসল কথা হচ্ছে সরকারের বরাদ্দ কৃত একশত ষাট কোটি টাকার শ্রাদ্ধ কিভাবে করা যায় সেটার পরিকল্পনা করা।,0,celebrity
"৩০ তারিখ পরীক্ষা তাই একটু হলেও মন খারাপ,ষ্যার আপনার পোষ্ট পড়ে আমি আমার হাসী ফিরে পেয়েছি।",0,celebrity
অন্যের সম্পর্কে মন্তব্য করার আগে নিজের যোগ্যতা বিচার করে নিন@mahmudul hasan,0,celebrity
আহা,0,celebrity
ধন্যবাদ স্যর।,0,celebrity
"yes, its a good decision.....",0,celebrity
স্যার আমি আপনার পোষ্টের কমেন্ট পড়া ফ্যান.... এখন কমেন্ট গুলা পড়বো সময় পেলে কয়েকঘন্টা পর আবার এসে পড়ার চেষ্টা করবো। হাসি-খুশী থাকলে শরীরের জন্য ভাল।,0,celebrity
আমি দেখলাম  উপরে অনেকেই  স্যারের কথায় সম্মতি দিয়ে কমেন্ট করেছেন কিন্তু তারা এতে সম্মতি দিয়েও আবার আগের মতই লিখেছেন এটা কেমন?,0,celebrity
সবাই সবার কমেন্টে হা হা রিয়েস্ট দেন,0,celebrity
"স্যার বেচে আছেন আলহামদুলিল্লাহ,, চোখে পানি চলে আসল😜",0,celebrity
"এরপর ১৯৯৬ সালে নির্বাচনে জিতে আওয়ামী লীগ ক্ষমতায় এসেছে। আমি তখন আমার স্ত্রীকে বলেছি, চলো, আমরা একটি টেলিভিশন কিনে আনি। এখন নিশ্চয়ই টেলিভিশনে বঙ্গবন্ধুকে দেখাবে। আমি আর আমার স্ত্রী পরিচিত এক বন্ধুকে নিয়ে বাজার থেকে টেলিভিশন কিনে এনেছি। সেই টেলিভিশনে বহুকাল পরে প্রথমবার বঙ্গবন্ধুকে দেখে আমাদের চোখ ভিজে এসেছিল। . কি কিউট আপনি স্যার। আমার চোখ ভিজে গেলো",0,celebrity
"আল কুরআন বলছে, যে বিষয়ে তোমার জ্ঞান নেই সে বিষয়ে চুপ থাক। জর্জ হাবার্ট বলেছেন, বেফাঁস কথা বলার চেয়ে চুপ থাকাই শ্রেয়। শেখ সাদী বলেছেন, একজন নির্বোধও ততোক্ষন পর্যন্ত জ্ঞানী, যতোক্ষন সে চুপ থাকে। . মানুষ কোন বিষয়ে তার দক্ষতা, পান্ডিত্যের জন্য খ্যাতি অর্জন করেন, জনপ্রিয় হন। জনপ্রিয় মানেই কিন্তু এমন না যে সে সব বিষয়ে পন্ডিত হবে। কিন্তু জনপ্রিয়তা ও গ্রহণযোগ্যতা অর্জনের পর কিছু মানুষ আর নিজেকে তার সীমার মধ্যে ধরে রাখতে পারে না, সব বিষয়েই পান্ডিত্য ফলাতে চায়, তখন সে জেনে-না জেনে, বুঝে-না বুঝে সব বিষয়েই মন্তব্য করে, আর এভাবেই তার পতনকে ত্বরান্বিত করে। . আজকের প্রকাশিত লেখাটির আগেও উনার একটা লেখা বেশ সমালোচিত হয়েছে। সেটা নিয়ে টু দ্যা পয়েন্ট লিখেছিলাম। আজ আর উনার অর্বাচিন সুলভ লেখা নিয়ে বিষদ কিছু লিখে সময় নষ্ট করবো না। জাস্ট একটাই চাওয়া_ আল্লাহ যেন উনাকে কিছু বলার আগে সেটা নিয়ে একটু জানা-শোনার করার তওফিক দেন, নাহয় চুপ থাকার তওফিক দেন। . মূলত বুকে/প্লেকার্ডে ""আমি রাজাকার"" টাইপ কথা লেখা নিয়েই উনার আজকের লেখাটা। উনি ভাবছেন এসব লেখে ছেলে-মেয়েরা চাকরি চাইতে এসেছে, রাজাকারদের অনেক বড় কিছু ভাবছে আজকের জেনারেশন। মেবি একটা পাগলও এভাবে ভাববে না। উনি হয়তো ব্যঙ্গ কি জিনিস সেটা বুঝেন না। অবশ্য বুঝবেন কি করে, উনি তো কুয়োর ব্যাঙ্গের মতো নিজের ক্ষুদ্র গন্ডির মধ্যে থেকে বিশ্বটাকে নিয়ে ভাবেন। উনি লিখেছেন, উনার প্রথম লেখাটা প্রকাশের পর উনি ছাত্র-ছাত্রীদের কাছ থেকে অনেক মেইল পেয়েছেন, যা উনি না পড়েই ডিলিট করে দিয়েছেন। উনি ফেসবুকেও বসেন না, উনি নাকি কিছু পত্রিকা পড়েন, আর সেসব পড়েই যা জানেন/বুঝেন সেটাকেই সব মনে করেন। উনি তো এর পক্ষে-বিপক্ষে পর্যালোচনাই করেন না। উনি আন্দোলন চলাকালীন এক টিভিতে বলেছিলেন, উনি নাকি জানতেনই না কোটার বিভিন্ন দিক সম্পর্কে।... উনি আজ তার লেখায় বলেছেন, উনি বুঝতে পারছেন না ""আমি রাজাকার"" টাইপ কথা লেখার পরও কোনও পত্রিকা কেন এর প্রতিবাদ করেনি?? উনি নাকি জানেন না অনেক দিন ধরে চলে আসা এই আন্দোলন ৮ এপ্রিলে এসে হঠাৎ এতোটা দানা বাধঁলো কিভাবে?? উনি নাকি বুঝতে পারছেন না হঠাৎ কেন সব জায়গার ছাত্রমহল এভাবে আন্দোলনে জড়িয়ে গেলো?... স্যার আপনাকে পরামর্শ দিবো আগে প্রশ্নগুলোর উত্তর জানার চেষ্টা করুন। একটু ভাবুন, বাস্তবতাটা উপলব্ধির চেষ্টা করুন। তাহলেই সব পরিষ্কার হয়ে যাবে, বুঝতে পারবেন কোন চেতনা থেকে পুরো ছাত্রসমাজ স্বাধীনতার এতো বছর পর আবার এক হতে পেরেছে। . পরিশেষে, জন্তুরা আহার পায় বাঁচে, আঘাত পায় মরে, যেটাকে পায় সেটাকেই বিনা তর্কে মেনে নেয়। কিন্তু মানুষের অন্যতম স্বভাব হচ্ছে মেনে না নেয়া। জন্তুরা বিদ্রোহী নয়, মানুষ বিদ্রোহী।",0,celebrity
নিশ্চিত থাকুন! ডাস্টবিনে পতিত হওয়ার সময় হয়ে এলো বলে,0,celebrity
"মুততে যাওয়ার জন্য রেডি হইসিলাম ; শুনলাম আপনি পোস্ট দিসেন, তাড়াতাড়ি পোস্ট পড়তে আসলাম ; তারপর বোকাচোদা হয়ে গেলাম -.-",0,celebrity
"পচাত্তরের ১৫ই আগষ্ট বঙ্গবন্ধুকে হত্যা করার মধ্য দিয়ে উল্টো পথে যাত্রা শুরু করে বাংলাদেশ। সাম্প্রদায়িকতাকে রাষ্ট্রীয়ভাবে, সামাজিকভাবে, পারিবারিকভাবে আমাদের ব্যক্তিগত জীবনে ঢুকিয়ে দেয়া হয়। সেই সাম্প্রদায়িকতার বিষবাষ্প থেকে আমরা এখনো মুক্ত হতে পারি নি। বঙ্গবন্ধু যে অসাম্প্রদায়িক বাংলাদেশের স্বপ্ন দেখেছিলেন তা বাস্তবায়ন করতে হলে বাঙ্গালী সংস্কৃতিকে তৃণমূলে ছড়িয়ে দিতে হবে। আমি বিশ্বাস করি যে শিশুটি গান গায়, যে শিশুটি নাচ শেখে, যে শিশুটি ছবি আঁকে, যে তরুণ/তরুণী টি থিয়েটার করে তারা কখনো সাম্প্রদায়িক হয়ে গড়ে উঠতে পারে না৷ আমরা অসাম্প্রদায়িক ভবিষ্যৎ প্রজন্ম গড়ে তুলতে পারলেই মুক্তিযুদ্ধের চেতনা বাস্তবায়ন হবে, সত্যিকারের সোনার বাংলা হয়ে উঠবে দেশটা।",0,celebrity
"স্যার আপনি একটা লেখা লিখছেন, ভালো। চেষ্টা চালিয়ে যান। তবে মঙ্গল গ্রহের চিপা গলিতে পৃথিবীর নায়িকা ডলির সাথে অই গ্রহের নায়ক ডলার ডলাডলি নিয়াই থাকেন। না হয় এই সব মৌলবাদী কমেন্ট পড়ে হরহর করে বমি করে দেবেন।",0,celebrity
হিহিহিহিহিহি 😂😂😂😂,0,celebrity
উনি অতিমাত্রায় তেলবাজি লেখক !! 71 সালে উনার যে বয়স ছিল উনি যুদ্ধে যেতে পারতো ?? কিন্তু এখন রাজাকার বলতে বলতে বেহুস !!! সাম্প্রতিক আন্দোলনে উনার ভূমিকা কি ছিল জাতি দেখেছে ???,0,celebrity
এ আইনটি বর্তমান সরকার প্রণয়ন করেছে সরকারি প্রতিষ্ঠানে স্বচ্ছতা ও জবাবদিহিতা নিশ্চিত করার জন্য। এটা মাননীয় প্রধানমন্ত্রীর অবদান। উক্ত বিষয়ে লেখার জন্য আপনাকে ধন্যবাদ।,0,celebrity
পাগল হইয়্যা গ্যাছে!,0,celebrity
আমার কাছেও দশ হাজার কোটি নিউরন আছে।আমিও কিছু করতে চাই...,0,celebrity
চমৎকার,0,celebrity
উঠেছেন ﻿ঘুম থেকে 😬 সুপ্রভাত স্যার,0,celebrity
"এক জঘন্য জানোয়ার জাফর ইকবাল, তার বাবা মা কি তাকে কোন শিক্ষা দেয় নাই!",0,celebrity
Sir...আপনারা যখন exam দিছেন তখন বই খুইলা লেখছেন।আর এখন আমরাতো আপনাদের মত এসব করি না।তারপরও আমাদের দোষ...  আপনিতো দেখছি Natok করতে গিয়ে ছবি কইরা লাইবেন।।।।।।  তাই বলছিযে ঘরে যান আর গাজা খাইয়া মন ও মাথার tension কমান....  আপনারে দেইখা আবারও বুঝলাম Bengali রা আজাইরা কাম লইয়া নাচে বুঝুক আর না বুঝুক।এত দিন কই আছিলেন....  মাল খাইয়া ঘুম দিছিলেন।।।।,0,celebrity
"কে যেন ফেসবুকে প্রচার করেছিল আপনি আর ইহজগতে নেই! আমি বিশ্বাস করিনি। স্যার মরতে পারেন না। আমার ধারনা সত্যি হল। স্যার ছিলেন, আছেন, থাকবেন, লিখবেন, নাচবেন, গাইবেন, জাতিকে উদ্ধার করবেন।",0,celebrity
মজা নেও.... Razu Hossain Bijoy Faisal Mahamud Salahuddin Ayubi Mohammad Foysal,0,celebrity
"আমাদের বাংলাদেশ যে পৃথিবীর অন্য দশটা দেশ থেকে ভিন্ন তার একটা বড় কারণ, মুক্তিযুদ্ধের পর এই দেশে অনেক মা ঘর থেকে বের হয়ে সংগ্রাম শুরু করেছেন। বেঁচে থাকার জন্যে সেই সংগ্রামের কথা কতোজন জানে? মুক্তিযোদ্ধারা যুদ্ধক্ষেত্রে যে যুদ্ধ করেছে মুক্তিযুদ্ধের পর আমাদের দেশের সেই মায়েদের যুদ্ধ তাঁদের থেকে কোনো অংশে কম নয়। আমরা কী সেটা মনে রাখি? ",0,celebrity
"স্যার আজকাল ঘুমে থাকেন, দিন তারিখের হিস্যেব থাকেনা। এইজন্য ৩তারিখকে ১ তারিখ ভেবেসেন। আপনারা এ নিয়ে রাজনিতি কত্তেসেন ক্যেঁন?",0,celebrity
চাটুকর😁,0,celebrity
আমার কাছে বঙ্গবন্ধু ও বাংলাদেশ অবিচ্ছেদ্য অংশ।,0,celebrity
"মতিয়া দিদার কথানুযায়ী আপনিও তো রাজাকার আপনার নিজের নামেই বইটা করতেন, নাম চেঞ্জ করেন স্যার।  আশা করি বেস্ট সেলার হবেন।",0,celebrity
উপযুক্ত বয়স থাকতেও আপনি কেনো মুক্তিযুদ্ধে যাননাই সে প্রশ্নের উত্তর কিন্তু বিভিন্ন জায়গায় আপনাকে করা হলেও উত্তর দেননি। আজও করলাম। উত্তর কি পাওয়া যাবে?,0,celebrity
চোরেরা নীতি কথায় নাকি খুব পটু হয়!! আর রাজাকারেরাও এখন মুক্তিযুদ্ধের বয়ান করে!!!,0,celebrity
আপনার জন্য কেয়া কসমেটিক এর পক্ষ থেকে মহামূল্যবান কমেন্ট ! 😂🔫,0,celebrity
"তুমি অনেক বড় দালাল বাংলাদেশ বুঝে গেছে,১৪ সালের নির্বাচন, গণতন্ত্র হত্যা, দূর্ণীতি, টাকা পাচার,গুম খুন,এগুলো আপনার আওয়ামীলীগের অর্জন। এদের কে মদদ দেওয়ার জন্য তোদের মত কিছু সুশীল দালালকে বিচারের মুখোমুখি করা হবে, ইনশাআল্লাহ",0,celebrity
"কমেন্ট পড়তে আইছি, স্টাটাস পড়ে পড়মু....",0,celebrity
এ লোক সুশীলতার মুখোশধারী আওয়ামী দালাল,0,celebrity
"সবাই ইতিবাচক চিন্তা-ভাবনা করুন...আসলে তিনিও নিরাপদ সড়ক চান...কিন্তু পোস্ট বড় হওয়ার কারণে লিখতে লিখতে দেরী হয়ে গেল আর কি...যাই হোক জানাযার আগে লিখে শেষ করেছেন তাও কম কি...লোকটি কেমন ছিলেন?কেউ ""ভাল ছিলেন"" না বলে যাবেন না...প্লিজ৷",0,celebrity
"অসাধারন সুন্দর একটি পোস্ট। পলাশীর মোড় থেকে টিএসসি চলাফেরা করলে, রাত বারোটায় সবারই মনে হয়, তিনটি সেরা বিশ্ববিদ্যালয় এ তল্লাটে থাকার পরও এখানকার আড্ডা কমেইনা, তাহলে পড়াশোনা আর গবেষণা কখন হয়?",0,celebrity
ধন্যবাদ স্যার তবে বড্ড দেরিতে।,0,celebrity
আল্লাহর কাছে আপনার সার্বিক সুস্থ্যতা কামনা করছি স্যার।,0,celebrity
"মিঁয়া ভালো কথা কউ বা বাজে, আমার শুধু আপনার লেখার উপর হরহর করে বমি করতেই ইচ্ছে করে!",0,celebrity
"সেনাবাহিনী থেকে মেজর জিয়া ক্ষমতায় এসে বহুদলীয় গণতন্ত্র প্রতিষ্ঠা করলেন অথচ শেখ মুজিব গণতন্ত্রের কথা বলে যুদ্ধ করে নিজেই পাকিস্তানি শাসকদের মত গণতন্ত্র হত্যা করলেন । জিয়াউর রহমান কোনো জামায়াত নেতা কে মুক্তি দেন নাই বা রাজনীতি তে নিয়ে আসেন নাই । উনি শুধু দেশ বিরোধী ও জনবিরোধী আইন গুলো বাতিল করেছিলেন । এতে আওয়ামিলীগ সহ জামায়াত, বামপন্থী দল গুলো রাজনীতি করার সুযোগ পায় ।",0,celebrity
২০০১ সালে জামাত বিএনপির সাথে জোট বাঁধে। তার আগে জামাত ইসলাম কোথায় ছিল ?? বিভিন্ন পত্রপত্রিকায় ছবি দেখেন নাই? দেখবেন কিভাবে  আপনারাতো একচোখা দালাল।,0,celebrity
"অপেক্ষায় আছি কোনদিন এই চতুষ্পদ দালাল টা মরবে.. সেদিন আমিও সবার মত পোষ্ট দিবো, ""বাঙালি গুণী লোকের কদর  দিতে জানে না.."" 🙄",0,celebrity
"কমেন্টে পড়ার জন্য আসি ,মনটা খুব খারাপ ছিল:-P",0,celebrity
এ লিখাটা আমার কাছে যুক্তিক মনে হয়েছিল কিন্তুু না আমি কেথাও ভুল করছি তাই হড়হড় করে ভুমি আসতে চাইল😜,0,celebrity
নিজেদের কেন রাজাকার বলেছে জানেন স্যার?? কারন মতিয়া চৌধুরী  এর বক্তব্য। স্যার মনে হয় মতিয়া চৌধুরী এর বিষয়ে অবগত নন।,0,celebrity
এতো বড় জিনিস যে হোগায় নিতে পারসো তোমারে ভ্রাম্যমাণ ব্যাংক হিসেবে ব্যবহার করা সময়ের দাবি।টাকা পয়সা অন্তত বাংলাদেশী ব্যাংকগুলা থেকে বেশি নিরাপদে থাকবে 🐸,0,celebrity
কাদের সিদ্দিকী বীর উত্তম এক অনুষ্ঠানে বলেছে আপনার বাবা রাজাকার ছিলেন? এবং এক পত্রিকায় আপনি সাক্ষাত কার দিয়ে বলেছিলেন যুদ্ধের সময় আপনি উঠানে মাটি গর্ত করে লুকিয়ে থাকতেন? পুরো বিষয়টা পরিষ্কার করলে খুশি হবো।,0,celebrity
"স্যার, আপনি নাকি সাইনটিস মানুষ। কি একখান কথা কইলেন, নারী - পুরুষ সমান। হেয়া কেমনে অয়???? Anatomically, physiologycally & phychiatrically হেরা পুরাই আলাদা।হেরাতো একজন আর একজনের সহযোগী (complement) মাএ ।হেগো ""নারী - পুরুষ সমান"" এই কলাটা দেহাইয়া হেগো লগে নিশ্চয়ই আপনে নাচানাচি করতে চান তাইনা????",0,celebrity
"আপনি বাইচা আছেন স্যার , আমরা তো ভাবছিলাম আপনি মইরা গেছেন ।",0,celebrity
"অরিত্রির মাথায় হাত বোলাতে পারেননি কিন্তু সেই মেয়েটির মাথায়তো হাত বোলাতে পারেন,যে মেয়েটি দুদিন আগে সংবাদ সম্মেলনে বললো ""আমাকেও গুম করে নিয়ে যান তাহলে বাবাকে দেখতে পাবো""। জানি স্যার! এখানে আপনি কিছু বলবেননা কারণ আপনার মানবতা এখানে কাজ করবেনা, আসল কথা হলো আপনি চাটুকার,মনুষত্যহীন। মানবতার কথা যেটা বলেন সেটা অভিনয়,সুবিধার জন্য বলেন। যদি মানবতা বাদী হন তাহলে এসকল শিশুদের কথা লিখুন।",0,celebrity
আজকে ১তারিখ না আজকে ৩তারিখ হয়ে গেছে🙂 সেফাত দাদুর মত মদ খাইছেন নাকি🐸,0,celebrity
আল্লাহ ভরসা Fiamanilla Get well soon sir,0,celebrity
"১৯৯৬ এর নির্বাচনকে 'ভোটার বিহীন' বলিলেও ৫ জানুয়ারির নির্বাচনকে 'ভোটার বিহীন' বলার হিম্মত হইল না জাফর ইকবাল সাহেবের !!  একটা গ্রহণযোগ্য নির্বাচন ব্যাবস্থা ধ্বংস করার অপরাধে যে হাসিনা দোষী, আর তারই হিংস্র প্রতিক্রিয়া আজ দেখছি।  আদালত যে এমিকাস কিউরি নিয়োগ করেছে তারা, নাগরিক সমাজ, সমস্ত বিরোধী দল সমূহ, এমনকি সরকারি এম্পিরাও যেখানে নির্বাচনের জন্য তত্ত্বাবধায়ক সরকারের পক্ষে মত দেয়। অথচ, হাসিনার একক সিদ্ধান্তে তা বাতিল হয়ে যায়। তার সাথে বাতিল হয় গন ভোটের অধিকার।  এসব নিয়েও একটু কমন সেন্স দেখান,  মশাই!!",0,celebrity
"ভাল মানুষের সাথে আল্লাহ্ সবসময় থাকে স্যার। যারা আপনাকে চিনতে পারেনি, আপনার উপর যে অমানুষগুলো এই হামলা চালিয়েছে তারা কোনদিন ভাল থাকতে পারবেনা। আপনাকে বাচানোর মাধ্যমে আল্লাহ্ প্রমাণ করে দিলেন যে তিনি ভাল মানুষের পাশে থাকেন। আপনি আরো অনেক বছর বেচে থাকুন স্যার। এই পৃথিবীতে আপনার মত ভাল মানুষ খুব দরকার।আমরা সবাই আপনার পাশে আছি 😊😊",0,celebrity
"বড় মানুষদের অসম্মান করাটা গৌরবের নয়, কমেন্ট করীরা, প্লিজ মানুষ সম্মান করতে না পাড়লে অন্তত অসম্মান করবেন না।",0,celebrity
"সুশীল মানে অপশিক্ষিত, ক্যারেক্টার লেস, দেখানো নাস্তিক, দেশের ভালো হলে শরীর জ্বালা-পোড়া করা, বিদেশি দালাল।",0,celebrity
"সত্য ও সুন্দর কথা স্যার। বলে মানুষকে শেখানো যায়, কারণ, মানুষ শিখতে চায় না, পড়তে ও জানতেও চায় না। মানুষের হাতে এত সময় যেমন নেই, তেমনি এত হালকা, সস্তা, সহজলভ্য উপায় তৈরী হয়ে আছে যে, কস্ট করে পড়ার ধৈর্য ও সুযোগ কোথায়!!  আমরা শুনার চেয়ে বেশি বলতেও শিখেছি। আসলে আমরা, আমড়াই। আপনাকেও বলেও যেতে হবে, আমরাও আমড়া....  ঢেঁকিই থাকবো।",0,celebrity
স্যার আপনি খুব শীগ্রই সুস্থ হয়ে উঠুন।এই দোয়াই করি,0,celebrity
স্যার... গম আছেন নি....আইতো মনে গইজ্জি তুয়াই গর্তত গেইয়োগ।।।।,0,celebrity
"আপনাকে লেখক হিসেবে যতটা শ্রদ্ধা করি, বাস্তবতা বিবর্জিত রাজনৈতিক কলামের জন্যে  কেন জানি মনের গহিন ঘৃণা তৈ‌রি হয়!  দেশের মানুষ কতটা কষ্টে আছে সেটা বোঝার ক্ষমতা আপনার এখনো হয়নি, তবে বিশেষ দলের জন্যে দালালি টা ভালো পারেন।",0,celebrity
স্ট্যাটাস টা পড়লে বমি হওয়ার সম্ভাবনা আছে তাই মদ খান আর কমপন্ট পড়েন।।।,0,celebrity
"কেউ বিচলিত হবেন নাহ,উনি মারা গেছেন,, তার জাহান্নাম কামনার জন্য আমিন লিখে যান",0,celebrity
"সার, কোচিং এসোসিয়েসন থেকে মন্ত্রণালয়ে নাকি গিফট যায়।",0,celebrity
ই বেটায় সপ্তায় একবার লেদে,0,celebrity
আপনাকে লাল ছালাম ।,0,celebrity
হরহর করে একটি পোস্ট এসে গেল 💝 ১৪৩ 🌹,0,celebrity
হেতেনের লেখা না পইড়া আইলাম আগে কমেন্ট পড়তে 😂😂,0,celebrity
এই সুন্দর পৃথিবীটা আপনাকে অনেক দিন ধরে আগলে রাখুক যতনে।আপনার সূস্থতা কামনা করি স্যার।,0,celebrity
এখানে নাকি ধোয়া ধুয়ি চলছে। কমেন্ট দিয়ে। দেখতে আসলাম।  😁😁,0,celebrity
আপনি না মারা গেছিলেন...??? 🤔🤔🤔 আমরা তো আপনার গায়েবি জানাযা পইড়া ফেললাম... 🙄🙄🙄 মইরা ও ফেবু ওয়াল চেক করেন..???,0,celebrity
"স্যার আমি শুনেছিলাম ছাত্রলীগরা নাকি একদিন আপনারে মারছিল,,তারপর আপনি নাকি বৃষ্টিতে ভিজে ছিলেন,,স্যার কথাটি কি সত্যি??",0,celebrity
"আমার বন্ধু রাশেদ উপন্যাসটা পড়েছি। সেখানে বৈষম্য দূর করার দুঃসাহসিক রাশেদের বর্ননা দিয়েছেন।  আমি রাশেদের নাম দিয়েছি সাহস ।এই সাহস জন্ম নিয়েছে কোটা বৈষম্য দূর করতে।এই সাহসকে নিয়ে আপনি কেনো,আপনার সাহিত্যকে সমৃদ্ধ করছেন না??????  আপনার লেখা পরে ,আমি হন্য হয়ে হাতুড়ি খুজছি,আমার মাথাডা ঠিক নাই,,,মাথায় একটা বারি দিতাম।  স্যার আপনাকে আহত করেছি।।স্যরি।।",0,celebrity
জাফর ব্রো :-D,0,celebrity
মুগো বাঙ্গালীরা  বেশ শিক্ষিত হইয়া গেছে।  তাই মুগো জাফর ইকাবাল স্যারের কমেন্ট বক্সে ডাইরিয়া হইয়া যায়। আজিব পুলাপাইন ‼,0,celebrity
"এই দেশ ধর্মান্ধদের যেমন নয় ,তেমনি ধর্মঅবমাননাকারীদেরও নয় ।খেয়াল করবেন স্যার , আমি কিন্তু নাস্তিকবলিনি , আস্তিকতা নাস্তিকতা এইটা যারযার নিজস্ব ব্যাপার । কিন্তু একটা মুসলমানরাষ্ট্রে থেকে মহানবী সঃ কে গালিগালাজকরে ব্লগ লেখা কি আসলেই ঠিক ।এইটা কি উস্কানি নয় । সুতরাং দোষ শুধুধর্মান্ধদের নয় । দোষ এইসবধর্মঅবমাননাকারীদেরও যারা কোন কারনছাড়াই ব্লগে কুৎসিত সবকথা লিখে বেরাচ্ছে । আপনার লেখারমধ্যে ধর্মান্ধদের প্রতি উপদেশ আছে , একটুধর্মঅবমাননাকারিদেরও উপদেশ দিন ।তাদের বলুন যাদের উন্নত মস্তিস্ক যেন দেশএবং দশের উপকারে লাগায় ।",0,celebrity
এই লোকটি এত বেশি চাটুকারিতা করে যে দেশের তৈলের দাম কমছে ই না। শিক্ষক এত লজ্জাহীন হয়?,0,celebrity
বাবাগো মড়া মানুষ  খাড়া হয়ছে 😨👻😱,0,celebrity
"ধিক্কার জানাই নিজেকে, আপনার মত মেরুদন্ডহীন, চাটুকারের লেখা বই পড়তাম একসময়। ছি ছি",0,celebrity
"কিছু মানুষ এক সময় এই লোকটাকে গালি গালাজ করতো কষ্ট পেতাম , ভাবতাম জাতির সূর্য সন্তানদের যারা গালিগালাজ করে তারা কোন লেভেলের মানুষ? আজকে আমি ভাবছি তারা ঠিক ছিল , আমি ভুল জগতে বাস করতাম। দুর্জন বিদ্ধান হলেও পরিত্যাজ্য।",0,celebrity
"""মীর জাফর"" নামটা আজ সার্থক আপনার! :)",0,celebrity
স্যার যারা অরিজিনাল রাজাকারের বাচ্চা তারা অাবার এখানে ওদের পরিচয় দিবে বিভিন্ন ভাবে ধন্যবাদ স্যার,0,celebrity
বাচ্চা ছেলেদের আন্দোলন বলতে কি বোঝাল জাফর ব্যালেন্স ইকবাল?? মানে সড়ক নিরাপদ খালি বাচ্চাদের দাবী??? ১৮ বছরের উপর কেউ বাসের চাপায় মারা গেলে তার লাইফ আবার রিস্টার্ট হয়???,0,celebrity
"দল যার যার , ভোট নৌকার ।",0,celebrity
কোন হ্লায় কোন হ্লায় কইছিল আমাদের চ্যার মারা গেছে.... আমিযে আবেগে গায়েবি যানাজা আদায় করলাম এহন হেইডার কি হইবো... Ahmed Naaeem...... দেখ আমাগো চ্যার এহনও জীবিত আছে...,0,celebrity
"এই প্রথমবারের মতো আপনাকে ভীষণরকম ভুল মনে হচ্ছে স্যার। আপনি ভুল বুঝেছেন। ছাত্ররা রাজাকার ট্যাগ নিয়ে গর্ব করেনি। তাদের রাজাকার ট্যাগ দেয়া হচ্ছিল বলে তারা অভিমান করেই ভেবেছিল  ঠিক আছে তারা তবে রাজাকার, তারপরও তারা আন্দোলন করবে। আপনার কি এই মাত্রাতিরিক্ত কোটা বৈষম্য অযৌক্তিক মনে হয়না স্যার?",0,celebrity
"আমার কোন মন্ত্যব নেই, শুধু চোখের কোনে দু' ফোঁটা জল......",0,celebrity
ভালো,0,celebrity
আপনার কোদালের লাইসেন্স আছে? পোলাপান ধরতে পারে।😂😂,0,celebrity
"একটা সময় আপনাকে অনেক শ্রদ্ধা করতাম।  কিন্তু বিশেষ বিশেষ কিছু সময়ে আপনার চেহারা দেখে বুঝলাম... আপনি আসলে নিজের গা বাঁচিয়ে চলেন। আপনার কাছ থেকে সবাই কিছু আশা করে। মানে করত, এখন তা অতীত।",0,celebrity
"যাক, বমির বেগ কমেছে তাহলে শেষ পর্যন্ত।🙂",0,celebrity
"ভালোবাসা নেবেন স্যার। আমাদের সৌভাগ্য, আমরা আপনার মতো একজন মানুষকে দিকনির্দেশক হিসেবে পেয়েছি। বাঙালি জাতির দূর্ভাগ্য, তারা আপনাকে এখনো বুঝতে পারেনি।  বেঁচে থাকুন প্রিয় স্যার, যতদিন ইচ্ছে. ..",0,celebrity
ভাইরে দারুণ  ভাবে সেইফ  খেললেন।,0,celebrity
শুধুমাত্র কমেন্ট পড়ে হতাশ আমি😂😂😂,0,celebrity
কুমা থেকে বের হয়ে গেলেন!! কিভাবে সম্ভব!!?? এমনতো কথা ছিলনা। আসার আর দরকার কি ছিলো?,0,celebrity
কে দিয়াছে আমাকে মেয়াদ উত্তির্ণ গাজা. তাহাকে পেলে করিব সেলাম. বৎস গাজা খেয়েছি পোস্ট এর তাড়নায়. মৎস বেচিয়াছি টাকার আশায়,0,celebrity
"বন্ধুTuhin Abdulla চিন্তা করস,কি অবস্থা ?  বর্তমান তরুন প্রজন্ম জাফর ইকবাল স্যারকে নিয়ে কি ভাবনা পোষণ করে!!!  আমি তো কমেন্ট পড়তে আইসা দ্বিদায় পড়ে গেলাম😜😜😜",0,celebrity
"দুঃখিত স্যার,পুরো লেখাটি পড়ার ধৈর্য্য আমার নেই।প্রেম-বিরহ নিয়ে লিখলে পুরোটাই খেয়ে নিতাম।",0,celebrity
বেশ কম লিখলেন 😉,0,celebrity
আমাকে কেউ এক গ্লাস চেতনা দেবেন 😉,0,celebrity
ষ্যার সোনাগাছির মুক্তিযুদ্ধা।,0,celebrity
এম এস রহমান সাজু,0,celebrity
"ইসলামের নবীকে গালি দিয়ে  ওরা বলে ""বাকস্বাধীনতা"", আর গালি দাতাকে হত্যা করে  অন্যরা বলে ""হাতস্বাধীনতা""। আমরা কই যাই স্যার?  এই স্বাধীনতার কি কোন সীমা থাকা উচিত না?",0,celebrity
"চলেন বৃষ্টিতে একটু মোচ ভিজাই,তাহলে দুর্বলতা কেটে যাবে",0,celebrity
"জাফর সাহেব ওটা কোটা বিরোধী নয় , কোটা সংস্কার আন্দোলন । কে কোথায় নিজেকে রাজাকার বলেছিল তার জন্য গোটা আন্দোলন প্রশ্নবিদ্ধ হতে পারে না । আর আপনি বলেছেন এটা চাকরি পাওয়ার আন্দোলন , কিন্তু এই আন্দোলনের মুলে রয়েছে যোগ্যদের অধিকার নিশ্চিত করা(অনেকে জানে যে তারা সরকারি চাকরি পাবে না , যেমন আমি ) ।  এই আন্দোলন মুক্তিযুদ্ধের চেতনার বাহিরে নয় , বৈষম্য তৈরি করতে মুক্তিযুদ্ধ হয় নি । গনদাবিকে গলা টিপে ধরতে মুক্তি যুদ্ধ হয় নি ।  জনাব জাফর সাহেব আপনি জনমতকে গুরুত্ব দেন না , মুক্তিযুদ্ধ কিন্তু বইপত্রের সেন্টিমেণ্ট না , এটা একটা মূল্যবোধ যার দ্বারা একটি জাতি এক হতে পারে ,জাতিয় স্বার্থে এক হতে পারে , আপনার মত সুবিধাবাদী বুদ্ধিজীবী নাম ধারিরা কেবল সেণ্টিমেন্টাকেই বেঁচে খাওয়ার চেষ্টা করছেন । সংখ্যাগরিষ্ঠ মানুষের দাবিকে উপেক্ষা করে মুক্তিযুদ্ধের সেন্তিমেন্ট টাকে ব্যাবহার করছেন । আপনারা শুদ্ধ হন , তারুণ্যকে লালন করার চেষ্টা করুন",0,celebrity
"হার্বাট সায়মন হয়ত এই বিষয়টা নিয়েও উদ্বিগ্ন ছিলেন সবাই স্বাধীনভাবে মত প্রকাশের অধিকার পাবে।আর সেটা কতটা ভয়ঙ্কর হতে পারে এখানে আসলে বুঝা যায়।আমার এই কীটগুলোকে দেখলে মনে হয়,গণতন্ত্র বিষয়টা সবার জন্য না আসলে।ভালবাসা জানবেন।",0,celebrity
"৭১ এ স্যারের ভূমিকা - প্রথমে খুঁজে বের করতে হবে আমার ছোট ভাইকে (জাফর ইকবাল)। শুনেছি, সে যাত্রাবাড়ীতে আছে। গর্তে বাস করে। যাত্রাবাড়ীতে আমার দূরসম্পর্কের এক মামা বাড়ির পেছনে গর্ত করেছেন। তিনি তাঁর স্ত্রী এবং দুই ছেলে নিয়ে গর্তে বাস করেন। জাফর ইকবাল যুক্ত হয়েছে তাদের সঙ্গে।  হুমায়ুন আহমেদ,-কত না অশ্রুজল।",0,celebrity
"স্যার,আপনি খুব তাড়াতাড়ি সুস্থ হয়ে উঠুন। এই কামনা করি।",0,celebrity
ভূউউউউউত! 😨,0,celebrity
"আমার প্রানের নবী হজরত মুহাম্মদ!(সঃ) নিয়ে যারা কটুক্তি করে ওরা নির্বোধ! যারা নামধারি মুসলমান তারা আপন সন্তানদের অছিয়ত করে যাবেন,মরার পরে কবরে রাখার ক্ষনে যেনো এই দোয়া না পড়ে--""বিসমিল্লাহি ওয়ালা মিল্লাতি রসুলুল্লাহ!"" যাকে তুচ্ছ করে অন্যের মন রক্ষা করে--তার মিল্লাতে আপনাকে সপে দেওয়া ভন্ডামি;আমার রসুলকে কটুক্তি-গালি দেওয়া মানে পরিপূর্ন নাস্তিক।",0,celebrity
এই যে ষাঁড়  এই ষাঁড় তোমাদের কে দিয়েছে কে দিয়েছে???   হুউউউউ,0,celebrity
হাইবারনেশন থেকে জাগলেন নাকি?,0,celebrity
দালালী করবেন করেন কে নিষেধ করেছে। আপনি মুক্তিযুদ্ধের ফিল্টার দিয়ে সবকিছু দেখেন অথচ আপনি মুক্তিযুদ্ধ করেন নি.... সাপলায় দিছেন মুরগী....,0,celebrity
লাভ রিএক্ট দেয় কোন বোকাসোদারা??,0,celebrity
you're right sir.but the present government won't help you because he's very ungrateful.i can u always say the truth,0,celebrity
"প্রটোকল ছাড়া বের হইয়েন না রাস্তায়, দেশের শতশত পোলাপান হড় হড় করে বমি করে দেবে আপনার গায়ে :)   এখন অন্য ইস্যুতে লিখে ভাল সাজতে চাইছেন, ঘটনার মোড় ঘুরাতে চাচ্ছেন, ঠিক মীরজাফরের মত....",0,celebrity
আসছি হা হা রিয়েক্ট দেওয়ার জন্য।,0,celebrity
"রাজাকার ইজ্জত আলীকে নিয়ে ডঃ জাফর ইকবাল বই লেখায় যারা ক্ষুব্দ হয়ে গালি দিচ্ছেন তাদের পরিচয় তারা নিজেরাই প্রকাশ করছেন । তাদের বাবা , দাদা , নানা ,  খালু , মামু কারা ? তারা যে ঐ রাজাকার  ইজ্জত আলী  রিক্রুটের সদস্য এই গালমন্দ দেখলেই বোঝা যাচ্ছে পরিস্কার ।",0,celebrity
যেই জাফর ইকবাল তাগড়া শরীর নিয়ে মুক্তযুদ্ধ না করে  ৭১ এ  মামার বাসার  খোঁড়া গর্তের ভিতর আশ্রয় নিয়ে লুকিয়ে থাকতো মুক্তিযুদ্ধ নিয়ে কথা বলার তার কোনো অধিকার নাই !,0,celebrity
স্যার আমারও খুব বই পড়তে ইচ্ছে করে অনেক জানতে ইচ্ছে করে...যখন যে বই পাই সাথে সাথে পড়ে ফেলি...বই মেলায় যেতে খুব ইচ্ছে করে...কিন্তু বই মেলা তো ঢাকার বাইরে এত সুন্দর ভাবে হয় না...এই গ্রামে থেকে নানা প্রতিবন্ধকতায় যাওয়া সম্ভব নয়...আমার ইচ্ছা অনিচ্ছা সবকিছু টিভির পর্দায় দেখে দেখে মিলিয়ে যায়...,0,celebrity
কমেন্ট এ প্রচুর বিনোদন আছে সময় পেলে পড়বেন :-D,0,celebrity
এখনও দেখি সবাই তাঁর লিখা ঠিকই পড়ে। ওনার হাবিজাবি(!) লিখা তো আপনাদের পড়ার কথা না।,0,celebrity
আসলে মালের মাথায় কোন মাল নাই...............যা আছে ...থাক নাই বা বললাম।,0,celebrity
wow ^_^,0,celebrity
"১) পৃথিবী এতো অবিশ্বাস্য সুন্দর? খোদা আমাকে এই অবিশ্বাস্য সুন্দর পৃথিবীটিকে আরো কয়দিন দেখতে দেবে? -মুহম্মদ জাফর ইকবাল, কথাসাহিত্যিক ও অধ্যাপক, শাহজালাল বিজ্ঞান ও প্রযুক্তি বিশ্ববিদ্যালয় ২) বনি ঈসরাইলরা যে আল্লাহর উপর ঈমান এনেছে আমিও সেই আল্লাহর উপর ঈমান আনলাম। -মি.ফেরাউন। (যখন নীল নদে ডুবে মরে তার পূর্বের উক্তি) বি:দ্র: কোথায় যেন একটু মিল পাওয়া যায়। আপনারাও কি পাচ্ছেন?",0,celebrity
আশা করছি জাফর ইকবাল স্যার নিজে এই পেজটি চালান না। তাহলে কিছু অসুস্থ মানুষের নোংরা কমেন্ট গুলো তাঁর পড়তে হবে না।,0,celebrity
"আমি কখনো ই আপনার পোস্টে মন্তব্য করিন,মন্তব্য গুলো পড়ি এবং বিনোদন খুঁজে পাই।কিন্তু এবার (হর হর করে বমি)মন্তব্য না করে পারলাম না।আসলেই আপনি দল কানা বা সুক্ষ্মদর্শী দালাল।আওয়ামীলীগ এর উপর জনগণ আস্থা রেখে বিশাল জয় উপহার দিয়েছে বললেন।আপনি কি আপনার বিবেকেটাকে মেরে ফেলেছেন?নাকি বিবেক বলে কিছু আপনি ধারণ করেন না।যদি বিবেকটাকে বিক্রি করে থাকেন তবে আপনি যা ইচ্ছে তাই করতেই পারেন।আল্লাহ আপনার ঘুমন্ত বিবেকটাকে সজাগ করে দিন।আর কিছুই বললাম না।",0,celebrity
প্রিয় স্যার....💜💜💙❤❤💝💗💙❤❤,0,celebrity
"স্ক্রিনশট নিয়া রাখি পরে যদি আবার লেখা এডিট করে!  বাউরে বাউ কাউরে বিশ্বাস নাই,  মন্ত্রী মিনিস্টারের গাড়িতে লাইসেংস নাই।",0,celebrity
অসাধারণ!,0,celebrity
"Your writing is always nice and informative but definitely not neutral. I read your previous post and the current one. Both are same. You like to talk about the effect of the problem but not the cause. Analyze both cause and effect, not simply one.",0,celebrity
অসাধারণ লিখেছেন স্যার..!,0,celebrity
হাসতে হাসতে বমি করে দিলুম😁😁,0,celebrity
বদমাইস একটা।,0,celebrity
"আজ কমেন্ট এ রিয়ার অভাব,, এর আগে ভাই রা রিয়াকে কত ভালোবাসছিলো,,,,,,,, রিয়ার জন্য ১০০ বালতি সমবেদনা",0,celebrity
"আপনার ভাগ্য ভালো আন্দোলনের কয়েক দিন গর্তে ছিলেন।তা না হলে শহিদুল আলম এর মতো আপনার ও এতোদিন ডিম থেরাপি দিত।যাহোক আমি কোন গুজব ছড়াতে আসিনি।বাদাম নিয়ে বসে আছি,বাদাম খাবো আর comment পড়ব।🤓",0,celebrity
এই বেরাজাল থেকে কবে আমরা মুক্তি পাবো( sir),0,celebrity
You r Jinius,0,celebrity
এখন আমি মদ খাবো আর কমেন্ট পড়বো😂😂😂😂,0,celebrity
আপনারা রাজাকারে বিচারগুলো পরিক্ষার সময় হলেই কেন শুরু করেন?,0,celebrity
"১।ঙ. বিষয়ে বলবো: আমার জানা মতে পৃথিবীর প্রায় সকল উন্নত দেশেই সব এলাকার স্কুল, কলেজগুলো প্রায় একই মানের। কাজেই যে যেই এলাকায়ই বাস করুক ছেলে মেয়েদেরও সেই এলাকার স্কুল, কলেজে ভর্তি করাতে হয়, আমাদের দেশের মতো তাতে যান জট সহ মা-বাবাদের দুশ্চিন্তাও প্রায় থাকেনা বল্লেই চলে। মিরপুরের কোন স্কুল বা কলেজ যদি উদয়ন বা ভিকারুন্নেসার সমান মানের হয় তবে সময়, যানজট ঠেলে ঐসব প্রতিষ্ঠানে যাওয়ার দরকার কি? কিন্ত কে করবে এগুলোর বাস্তবায়ন !",0,celebrity
পপকর্ণ নিয়া কমেন্ট পড়তে বসলাম। বউকে হালকা ছোলা আর পেয়াজু ভাজতেও বলে দিসি।,0,celebrity
"আপনাকে অপছন্দ করা ব্যক্তিরাই আপনার পোষ্টে লাইক কমেন্ট করে তারা ভুল ধরার জন্যই,,,, নিজের ভুল হারিয়ে ফেলে।",0,celebrity
সাইকেল_ চালাচ্ছিলাম পোষ্ট টা দেখে খাদে পরে গেলাম উদ্ধারকারীরা আমাকে উদ্ধার করতে এসে পোষ্ট টা দেখলো তারাও হাসতে হাসতে খাদে পরে_গেল __  Cltd.,0,celebrity
মহাজাগতিক কিউরেটররা যদি পিঁপড়া না নিয়ে আপনাকে নিয়ে যেতো তাহলে পৃথিবীবাসী এই বিনোদন মিস করত।,0,celebrity
"অবিলম্বে ইনডিয়ান টিভি চ্যানেল #LifeOk এর সম্প্রচার বাংলাদেশে বন্ধ করুন এবং করতে হবে। এই চ্যানেলটির প্রোগ্রাম, অপরাধ করতে প্ররোচিত করে। তরুন সমাজের অপরাধ করার প্রবনতা বেড়ে যাবে। আপনার-আমার একার পক্ষে সব টিভি চ্যানেল এর সম্প্রচার নিয়ন্ত্রন করা সম্ভব নয়, তাই আন্দোলনে নেমছি, যদি আপনি দেশকে ভালবেসে থাকেন তবে সবাই একত্রিত হই। ঐ চ্যানেলের সম্প্রচার বন্ধ করেই তবে শান্ত হব।Everyone please share this message/post with all friends, pages, wall & comments box!!! www.facebook.com/tvchannelsviewers.Bangladesh",0,celebrity
কসম কমেন্ট পড়ে চলে যাবো......,0,celebrity
২৯ জন মানুষরূপী পশু এই পোস্টটিতেও হাহা রিয়্যাক্ট দিয়েছে!😣,0,celebrity
আপনার লিখা সেদিন থেকে পড়া বন্ধ করে দিয়েছি যেদিন থেকে কোটা আন্দোলন এর বিপক্ষে বলেছেন,0,celebrity
আপনাকে নিরপেক্ষ আশা করেছিলাম | জামায়াতের সাথে জোট তো নিজ নিজ স্বার্থে প্রধান দুটি দলই করেছিল | তখন তাদের এসব কথা মনে ছিলনা??,0,celebrity
"কোটা আন্দোলন নিয়ে আপনি ছাত্রসমাজের গায়ে যে হরহর করে বমি করেছেন, ছাত্রসমাজ তা কোনদিন ও ভুলবে না।",0,celebrity
"শুভ জন্মদিন,স্যার। ভালো থাকবেন।",0,celebrity
দয়া কইরা ষাড়রে কেউ লাল কাপড় দেখায়েন না পিলিস🐄🐄🐄,0,celebrity
"বাংলাদেশে সবচেয়ে বেশী কার পোষ্টে একজনের কমেন্ট দশে মিলে পড়ে?কমেন্ট পড়বি ত মানুষ হবি,,",0,celebrity
আপনার লেখাটি পড়লাম। নতুনরা কোথা থেকে শক্তি পেয়েছে? আপনাদের কাছ থেকে স্যার। Keep on writing sir. Never stop. নতুনদের আরো শক্তি দরকার।,0,celebrity
"লিখা শেষ দায়িত্ব শেষ, এবার  আবার গর্তে  ঢুকে পড়ুন নাহলে মানুষ আপনার গায়ের উপর হড়হড় করে বমি করে দিবে 😂",0,celebrity
আমার উপর খেপলি ক্যান?,0,celebrity
স্যার কেমন আছেন 😊😊😊,0,celebrity
গর্ত থেকে বহির হইছে,0,celebrity
কমেন্ট পড়তে আইছি😄,0,celebrity
"তোমরা স্যারকে নিয়ে যে এসব বলছো, জীবনে কখনও স্যারের পায়ের সমানও হতে পারবে? ক্ষমা করবেন স্যার। এই নির্বোধ জাতি আপনার মূল্য দেওয়ার মত জ্ঞান রাখে না",0,celebrity
"তার মুখে দিয়ে যদি এ কথাটি আসতো,,আল্লাহ আপনি আমাকে মাপ করে দেন,,",0,celebrity
"হাসাইলেন স্যার, যেই বিমানবন্দরে আপনাকে চেক করা হয় না, সেই বিমানবন্দরই নিরাপদ!?",0,celebrity
ধন্যবাদ শ্রদ্ধেয় স্যারকে।,0,celebrity
স্যাড় হেলিকপ্টার বড়ই আজব জিনিস ! তেঁতুল হুজুর হেলিকপ্টারে চড়ে পটে গেছেন আপনিও হেলিকপ্টারে  চড়ে সি এম এইচ যাওয়ার পর পটে গেছেন | অতএব হে জাফর সাড় তুমি হেলিকপ্টারের কোন কোন অবদানকে অস্বীকার করবে ?🐸🐸,0,celebrity
আমাদের দোয়া আল্লাহ কবুল করেছেন কি না জানিনা।তবে মৃত্যুর দ্বারে এসে সুন্দর পৃথিবীটাকে উপলব্ধি আর হৃদয় নিংড়ানো আকুতি (বেঁচে থাকার জন্য) আল্লাহ মনে হয় কবুল করেছেন। দীর্ঘ ও সুন্দর জীবন কামনায়...।,0,celebrity
"you are right,sir.",0,celebrity
রাত এ ভাল করে ঘুম হয় নি স্যার এর।।।,0,celebrity
চেতনা তোর ব্যাক সাইডে ভইরা রাখ। দেশে নির্বাচন না নির্বাসন হইছে।,0,celebrity
"স্যার আপনাকে অনেক ভালবাদি,ভালবাসি আপনার মত স্বপ্ন পাগল মানুষকে। খোদার কাছে খুব করে চাই যে, আপনাকে খোদা তার খাস বান্দা হিসেবে কবুল করুন।",0,celebrity
"আহা! নন্দলালের জেরক্স কপি।  এত কষ্ট বুকে চেপে রেখেও বেঁচে আছেন এটাই অনেক।আবেগে দুচোখ দিয়া চার টন কান্না করে দিছি। বাই দ্যা ওয়ে,দিনাজপুরে বাতাবি লেবুর ফলন কেমন তা আপনি থাকতে বিটিভির মতো চ্যানেল ক্যামনে প্রকাশ করে বুঝিনা!",0,celebrity
একজন ভক্ত হিসেবে স্যারের কাছে আকুল আবেদন জানাচ্ছি-দয়া করে কোন ধরনের রাজনৈতিক মন্তব্য করবেন না।এই দেশের রাজনিতির ঘোলা জলে আমরা আপনার মতো মানুষকে দেখতে চাই না।,0,celebrity
কমেন্টে এসে দেখলাম সবাইতো বাংলা ভাষা শিল্পের দারুণ চর্চা শুরু করেছে😁😁😁😁😁😁😁,0,celebrity
"ছিঃ ছিঃ থু থু হাসিনা, আর নিচে নামিস না  জাফরুল্লাহ চৌধুরী কে, কি করে আমরা কি জানি না ?  যতই নিচে নামছিস ততই বাড়ছে তোর আর তোর দলের প্রতি ঘৃণা",0,celebrity
চেতনায়ে ডু,0,celebrity
ওপারে ভালো থাকবেন জনাব -,0,celebrity
আপনাকে অভিবাদন জানাই।,0,celebrity
"আপনি ভাষা ভাষা নিয়া এতো ফেনা তুলছেন, অথচ এই আপনিই কি করে পারলেন রাবা খানের বান্ধobi,বইটার প্রমোট করতে? যেখানে ভাষাকে বিকৃত ও ইংরেজী উর্দু হিন্দির মিশ্রনে জগা খিচুড়ি বানিয়ে মাতাল টাইপের ফালতু একটা বই বানানো হইছ!!!",0,celebrity
ব্রাজিল এর খেলা দেখে এই লেখা পড়লাম। সব কিরকম উল্টা পাল্টা লাগতেছে।,0,celebrity
ইচ্ছে করছে পদ্মা সেতু থেকে ১ টা পিলার এনে স্যারের পা...ছার ভেতর ঢুকিয়ে খাড়া করে রাখি। কিন্তু সরকারের উন্নয়নের চিএ কমে যাবে বলে কিছু করলাম না।,0,celebrity
"ইসলাম  ধর্ম  তোমাদের  চূলকানী  রুগ , ধর্ম  নিয়ে  কথা  বলার  সাহস  কে দিয়েছে  তোদের । এর নাম মুক্তমনা ???",0,celebrity
হড়হড় হড়হড়!,0,celebrity
বালের কোঁদাল,0,celebrity
বানানে ভূল করবেন্না প্লিজ😊,0,celebrity
"দেশ এখন অনিরাপদ।।স্যার,যাত্রাবাড়ীর গর্তটার সন্ধান যদি দিতেন।।।",0,celebrity
আচ্ছা খানকির পোলা যেদিন সিরাজ শিকদারকে হাতকড়া লাগিয়ে চোখ বাঁধা অবস্থাতে মারলো সেদিন তুই কই ছিলি ইন্ডিয়ার গোয়ার ভিতর না হাসিনার পেটিকোটের ভিতর,0,celebrity
আল্লাহ আপনাকে দ্রুত সুস্থ করে দিবেন এই দোয়াই করি। আপনাকে আমাদের বাংলাদেশে অনেক দকার আছে।,0,celebrity
yes sir,0,celebrity
"ক্ষমা করবেন, একটু খটকা রয়েছে। মনে হয়, দেশের নাম ‘ভারতবর্ষ’ নয় - শুধুই ভারত হবে। আর ভারত এবং বাংলাদেশের জাতীয় সঙ্গীতের রচয়িতা একজন হলেও দু’টোই বাংলা ভাষায় - এ তথ্যও সঠিক নয়। মনোযোগ দিয়ে শোনার অনুরোধ রইলো।",0,celebrity
আপনার পর্দার আড়ালে কিছু অপকর্ম আছে যা মেনে নেয়ার মত না।,0,celebrity
পানি খেয়ে লিখতে বসলেন নাকি । জামাত বিএনপি কৈ,0,celebrity
লেখালেখি করতে গেলে যদি লাইসেন্স-এর প্রয়োজন হতো তাহলে বাচ্চারা এতক্ষণে আপনার লাইসেন্স খোজত। যাক বেঁচে গেলেন।,0,celebrity
স্যার এইবার নির্বাচন দাড়ালেন না কেন?  গরিবের শিক্ষামন্ত্রী না হয়ে সত্যিকারের শিক্ষামন্ত্রি হতেন। আপনাকে ভোট দিয়ে যেতাব বলে ভোটার হতে চাইছিলাম,0,celebrity
"এই পিচ্চি গুলাই ত একসময় বড় হবে।ভাবতেও অবাকলাগতেছে,এরাই চুরি করা শিখে বড় হইতেছে???",0,celebrity
অরে বাবারে!!! স্যারের ঘুম ভাঙসে!!! দেশ উদ্ধার হয়ে গেছে। সবাই মোনাজাত ধরেন আর স্যারের জন্য দোয়া করেন।,0,celebrity
গ্রামার শেখার সহজ উপায় !! https://www.youtube.com/bdhomeschool,0,celebrity
আর কয়টা হাহা রিয়েক্ট খাইলে আপনি এসব রম্য পোস্ট দেয়া বন্ধন করবেন? :) 👉👌,0,celebrity
ভাই ও বোনেরা হুরাহুরি করবেন না! সবাই সিরিয়ালে দাড়ান....,0,celebrity
"আমি Normally বই টই কম পড়ি, কারণ যারাই বেশি বই লেখে বা পড়ে তারাই নিজেদের সবচেয়ে বুদ্ধিজিবি বলে জহির করে! আমার নিজের কোন কোটার প্রয়োজন নেই, কিন্তু এই আন্দলনের সাথে একাত্ততা ছিল। আপনি যদি মতিয়া Madam এর উক্তিটা সম্পুরন শুনতেন তাহলে লেখাটা হয়ত অন্যভাবে লিখতেন!  আর যদি সেটা শুনেও, বুঝেও এই Post টা লিখেন, তাহলে আপনি একটা যে আপদও মস্তক চাটুকার সেই বিষয়ে কোন প্রকার সন্দেহ নেই।  সেদিন আপনার মত মানুষ এর উপর ছুরিকাঘাত করার খবর শুনে খুব খারাপ লেগেছিল আর আজ আপনার এই লেখা টা পড়ে আরো বেশি খারাপ লাগছে, আপনিও শেষ পর্যন্ত ণিজের বিবেক কে খেয়ে দিলেন! আর এক টা বিশয় আপনার কাছ থেকে জাতি এই ধরনের Non-Sense লেখা আশা করেনা, At Least এত গুলো Comment পড়ে সেটা অনুধাবন করতে পেরেছেন!",0,celebrity
আজকে বিকাল ৫ঃ৩০ মিনিটে আপনার গায়েবানা জানাজা অনুষ্ঠিত হবে।  সময় মত চলে আসিয়েন।,0,celebrity
সবুজ ভেলভেট'।,0,celebrity
হড় হড় করে বমি আসতেছে। এভোমিন দেন ভাই কেউ,0,celebrity
"আন্তর্জাতিক মানের বিচার করতে যদি শরমই লাগে তাইলে ট্রাইবুনাল এর নাম - ""আন্তর্জাতিক যুদ্ধপরাধ ট্রাইবুনাল"" রাখা হলো কেন??  ট্রাইবুনালের নামের শুরুতে আন্তর্জাতিক শব্দটা জুড়ে দেয়া হলো কোন দুরভিসন্ধিতে???  আর আমাদের হাগা মুতা কার্যক্রম যেহেতু আন্তর্জাতিক মানের না, আমরা যেহেতু খাড়াইয়া মুতি না সেহেতু বাঙ্গালির আন্তর্জাতিক মানের বিচারের দরকার নাই, তো বিচারের কি দরকার ছিল, ডাইরেক্ট ঝুলাইয়া দিলেই পারতেন, এত নাটকের কি দরকার ছিল.....??? আপনি কি জানেন আপনাকে মানুষ বুদ্ধিজিবির পরিবর্তে বুদ্ধি বেশ্যা ডাকে???  নুন্যতম কমন সেন্সও আপনার মধ্যে নাই.... বাইদা ওয়ে ৭১ সালে আপনার নিজের ভূমিকা আপনার মনে আছেতো???  নাকি আরেকবার মনে করায়া দিব....??? :-P",0,celebrity
আমি এংরাজিতে কুপ কাচাঁ পিলিগ  OX মানে কি কেউ বলবেন।,0,celebrity
ধন্যবাদ স্যার।,0,celebrity
বাজে কমেন্ট পড়ে মনে হয় আমরা মূর্খের দেশে আছি,0,celebrity
"স্যার একটা প্রশ্ন ছিল।১৯৭১ সালে পাকিস্তান ছেড়ে বাংলাদেশ করার সবচেয়ে বড় যে কারণ ছিল তা হলো বৈষম্য। পাকিস্তানের বৈষম্য নীতি হতে বেরিয়ে একটা সাম্য মৈত্রী র সমাজ প্রতিষ্ঠা, সবাই যেন সমানাধিকার পায়। সমানাধিকার এর সবচেয়ে বড় উপায় কাজের বা যোগ্যতার ভিত্তিতে কারো বিচার করা। আচ্ছা স্যার মানলাম আমি মুক্তিযোদ্ধা এটা আমার যোগ্যতা কিন্তু আমার বাবা বা আমার দাদা মুক্তিযোদ্ধা সেটা কি আমার যোগ্যতা?",0,celebrity
"জাফর ইকবাল আজকে দৈনিক যুগান্তরে একটি কলাম লিখছেন।  সেখানে তিনি উল্লেখ করেছেন।  - ""ঢাকা শহরের মানুষকে জিম্মি করে আন্দোলন করার জন্য আমি যথেষ্ট বিরক্ত হয়ে সাপ্তাহ দুয়েক আগে একটি লেখা লিখেছিলাম।  (সে সময়ে আমার মেয়ে হাসপাতালে ছিল, তাই ঢাকা শহরকে জিম্মি করে ফেললে হাসপাতালের রোগীদের কী ধরনের কষ্ট হয় আমি নিজে সেটি জানতে পেরেছি)  একজন মানুষ কতখানি হিপোক্রেট হতে পারে, তাঁর জ্বলন্ত উদাহরণ হচ্ছেন এই জাফর ইকবাল।   আজকে উনার নিজের মেয়ে হাসপাতালে ছিল বলে উনি ফিল করতে পারছেন রাস্তা জিম্মি হলে কতখানি কষ্ট হয়। কিন্তু, উনি কলাম লিখে, বক্তব্য দিয়ে এক সময় এই তরুণ প্রজন্ম কে  ""ফাঁসি চাই"" স্লোগান দেয়ার জন্য রাস্তায় নামতে উস্কে দিয়েছিলেন। সেদিন জাফর ইকবালের মনে ছিল না, এই শাহবাগে দেশের বড় দুইটি হাসপাতালে চিকিৎসা নেয়ার জন্য দেশের দূর দুরান্ত থেকে প্রতিদিন অনেক বাবা তাঁর মেয়েকে নিয়ে আসেন।    কোটা আন্দোলনের ছাত্ররা ন্যার্য দাবীর জন্য রাস্তায় নেমে আন্দোলন করলে জাফর ইকবালের মানুষের দুর্দশার কথা মাথায় আসে।  কিন্তু মাত্র চার মাস আগেও উনার কাছে এই বিষয় গুলো কষ্টের ছিল না।  প্রধানমন্ত্রী শেখ হাসিনাকে সংবর্ধনা দেয়ার অনুষ্ঠানে জাফর ইকবাল যখন সহরোওয়ার্দী উদ্যানে আকাশ বাতাস প্রকম্পিত করে  ""জয় বাংলা"" স্লোগান দিছিলেন,ঠিক সেই সময়ে বাংলা মোটরে প্রচণ্ড জ্যামের মধ্যে ছটপট করছিলো একজন প্রসূতি মা।   এমন ন্যাক্কার জনক ঘটনার প্রতিবাদ দেশের বিবেকবান সকল মানুষ করলেও, জাফর ইকবাল সেদিন ব্যাস্ত ছিলেন ""বঙ্গবন্ধু উপর থেকে আমাদের সব অর্জন দেখছে"" কলাম লিখায়।   জাফর ইকবাল তাঁর বিবেক বন্ধক রেখে, মুক্তিযুদ্ধের চেতনা নামের এক কালী দিয়ে  কলাম লিখেন একটি স্বীকৃতি প্রাপ্ত স্বৈরাচার সরকারের জন্য। তাই উনার লিখায় কেবল স্বৈরাচারের স্বার্থ উঠে আসে, উঠে আসে নিজের স্বার্থের কথা। যেখানে উনি উল্লেখ করেন না, মুক্তিযুদ্ধ করে দেশ স্বাধীন করে এখন ভিক্ষা করা বীর আব্দুর রাজ্জাক শেখের কথা।  সেখানে উনি কোনদিন উল্লেখ করে না স-মিলের ভ্যান চালিয়ে সংসার চালানো বীর শ্রেষ্ঠ রুহুল আমিনের ছেলের কথা।   আমি অন্তর থেকে ধন্যবাদ জানাই কোটা আন্দোলন গ্রুপের সকল মেম্বার কে। আজকে সকাল থেকে সেখানে লক্ষ লক্ষ ছাত্র-ছাত্রী জাফর ইকবালের প্রতি তাদের চরম ঘৃণা জানিয়ে যাচ্ছেন। এই প্রজন্ম এখন জানে,বুঝে ছোট বেলায় পড়া প্রিয় কিশোর উপন্যাস লেখক জাফর ইকবাল একজন হিপোক্রেট।  যারা এখনো জাফর ইকবাল কে চিনতে পারে নাই।ইনশা'আল্লাহ তারাও একদিন চিনে যাবে।  অমানুষ চিনতে না পারলে লজ্জা পাওয়ার কিছু নাই। কারন অমানুষ গুলো দেখতে অবিকল মানুষ রুপী জাফর ইকবালের মতই হয়।  কপি : রাশেদ ভাই।",0,celebrity
"পোষ্ট কিন্তু পড়ি নাই, তাড়াহুড়ো করে সোজা কমেন্ট পড়তে আসলাম😝😝",0,celebrity
"বাঙ্গালী মহৎ আর যোগ্যতার যোগ্য ব্যাক্তিবর্গের কথা না বুঝে মূর্খ আর অযোগ্যের কথা মানে, কারণ মূর্খের কাছে আছে ক্ষমতার লাঠি যা দিয়ে দেশকে নিয়ে যাবে নিম্নমানের দিকে। উপরের বক্তব্য কারো কাছেই গ্রাহ্য মনে হবে না। এমন অনেকেই আছেন যারা বলবেন #জাফর_ইকবাল একজন পাগল। আসলে ভালো কথা কারো কাছেই ভালোলাগে না। আরে ভাই উনি ত উনার নিজের জন্য কথা বলেন নাই উনি বলছেন আমাদের কথা, আমাদের সুন্দর ভবিষ্যৎ এর কথা। এমন অনেক পরিবারের সন্তান আছে যে কোনো ভাবে কষ্ট করে এইচএসসি পরীক্ষা পাশ করেছে ভালো ফলাফল অনুযায়ী। কিন্তু সে যেকোনো একটি বিশ্ববিদ্যালয়ে পরীক্ষার জন্যও সামর্থ নাই। তবে কি করে সে ঘুরে ঘুরে বিশ্ববিদ্যালয়ের জন্য পরীক্ষা কি করে দিবে।।।।।।  তাই আমার মতে #জাফর_ইকবাল স্যারের কথার সম্পূর্ণ যুক্তিযুক্ত।।।।।",0,celebrity
ডক্টর শহিদুল এর উপর অত্যাচার অবিচার হচ্ছে আমেরিকা প্রবাসী ভাগিনার প্রত্যক্ষ নির্দেশে।  পুলিশদেরকে সচিব বানিয়ে খুশি রাখা হয়েছে।,0,celebrity
@ এডমিন -পাবলিক কমেন্ট গুলা এই পেজ এ পোস্ট হওয়ার আগে এডমিন কর্তৃক filtering হওয়া উচিত ! নতুবা অনেক কুরুচিপূর্ণ লোকের বাজে কমেন্ট পেজ এর পবিত্রতা নষ্ট করবে বা ইতিমধ্যেই করছে ! যেহেতু এই সব কমেন্ট স্যার এর চোখে পরার সম্ভাবনা আছে তাই এই বেপারটা আমাদের খেয়াল করা উচিত !,0,celebrity
সেই সময়ের জাফর ইকবালের আর আজকের দুই দিনের শিশুর ভিতরে কোন অমিল নাই কারন তিনি মুক্তিযোদ্ধার সময় ১৯ বছরের যুবক হয়েও ভয়ে পালিয়ে বেড়িয়েছেন আর মুক্তিযোদ্ধার ইতিহাস গুলো বই পুস্তক আর লোক মুখের  গল্পের মাধ্যমে জেনেছেন আর সে গুলো নিয়ে এত চ্যাটাং চ্যাটাং কথা বলছেন তার মুখে মুক্তিযোদ্ধার ব্যাখ্যা মানায় না,0,celebrity
আপনার মেয়াদঊত্তীর্ন weed(গাঁজা) এর ঘোর কি কাটছে......? না আবার এক কল্কি খাইছেন.....?,0,celebrity
গায়েবি জানাজারের ইভেন্টের ভয়ে পোষ্ট দিতে এসেছে যদি আবার যদি কেউ শ্মশানে ভুল করে না যায়🙂,0,celebrity
এইসব কমেন্ট পড়ে বোঝা যায় আজও বাংলাদেশে রাজাকারের বিজ বিদ্যমান। এমনও শুনেছি রাজাকারের সাহায্যেই নাকি এই দেশ স্বাধীন হয়েছে!তারাই নাকি মুক্তিযোদ্ধাদের সঠিক পথ দেখিয়েছে! জিয়া একজন প্রকৃত দেশপ্রেমিক ছিলেন এবং ছিলেন মুক্তিযোদ্ধা। তাতে সন্দেহ নেই কিন্তু কোন রাজাকারের অবদান তার পেছনে তা জানিনা!,0,celebrity
আপনার বলা কথগুলো আমরা ও একসাথে বলতে চাই এ লিখার জন্যে আপনাকে শ্রদ্ধা জানাই সার,0,celebrity
you are an idiot- you should not go after prothom alo,0,celebrity
Will someone give me tips on how to write in Bangla.,0,celebrity
ঈমানে দৃঢ় হন অাল্লাহকে সিজদা করুন জীবন মৃত্যু অার সুন্দর লাগবে স্যার।। অাল হামদুলিল্লাহ।,0,celebrity
"মদ খান, ঘুম দেন।",0,celebrity
"আর মাত্র ১৫০ টি হাহা রিঅ্যাক্ট চাই এই পোস্টে। তাহলেই লাইক এর চেয়ে হাহা রিঅ্যাক্ট বেশি হবে :-P  এখন হাহা রিঅ্যাক্ট 4k, আর লাইক 4.1k :-P",0,celebrity
"ষ্যারের চেতনা দন্ড দাঁড়াইয়া গেছে,,, ষ্যার গর্ত থেইকা বাইর হইছে এখন তিনি মুক্তিযুদ্ধের গল্প শুনাবেন😜😜😜😂😂😂",0,celebrity
ভাই সোলোগান দিয়েন না!! 🙊🙊,0,celebrity
wow... sir er jonne emon ayojon dekhe valo laglo.. shuvo jonmodin sir..,0,celebrity
ক্ষনিকের পুত্র,0,celebrity
"ছাত্ররা নিজেদের কেন রাজাকার বলেছে আর কোটা বাতিল না সংস্কার !!  এই দুইটা ব্যাপার না জেনে যদি লিখাটি লিখেন তাহলে নিজের চশমা পরিষ্কার করেন আর সব জানার পরও যদি লিখেন তাহলে চশমাটা আজীবনের জন্য খুলে রেখে দেন ।  (বাকি অনেক কথা বললাম না ।  অনেকেই বলেছে)  শেষকথা হচ্ছে, বুদ্ধিজীবী নিশ্চয় এমন হয়না!!!",0,celebrity
অনেক ভালোবাসা রইলো। আপনার সুস্থতা কামনা করি।,0,celebrity
বৎস এতোদিন পর একটা পোস্ট প্রসব করিয়াছো তা আবার উপন্যাসের মতোই...  মদ খাও মানুষ হও...,0,celebrity
ও রীমা,0,celebrity
আপনার লিখা পড়ে আমারো বুকটা ধুক করে উঠলো :|,0,celebrity
"চুলকানির নতুন মলমের নাম "" মীর জাফর ইকবাল """,0,celebrity
"Sajeeb Wazed::  বিএনপির পক্ষ থেকে আজ বলা হয়েছে যে জাতির জনককে স্বপরিবারে নির্মমভাবে হত্যা করার দিনে খালেদা জিয়ার ভুয়া জন্মদিন পালন করতে তাদেরকে নাকি বাধ্য করা হয়েছে। এটা কি সত্যিই তাদের যুক্তি? তাদের কোন লজ্জা নাই, নাই কোন চরিত্র বা নীতি। এটি মানবতাহীন বা নৈতিকতাবিহীন মানুষের একটি দল।  http://bangla.bdnews24.com/politics/article835749.bdnews  কেন আমাদের নির্লিপ্ত থাকতে হবে যখন তারা জাতির জনক এবং অবশ্যই পুরো জাতিকে তাদের জাতীয় শোক দিবসে অপমান করবে? কেন আমার পরিবার এবং আমাকে এই ধরনের পৌনঃপুনিক অপমান বছরের পর বছর সহ্য করতে হবে? আর কী করলে আমরা প্রতিক্রিয়া দেখাতে পারবো?  যদি তারা আওয়ামী লীগের বক্তব্যের কারণে এই জঘন্য জিনিসটি করতে বাধ্য হয়, তবে একইভাবে আমাদেরও তাদের প্রতি প্রতিক্রিয়া দেখাতে দেয়া উচিৎ।  জয় বাংলা জয় বঙ্গবন্ধু।",0,celebrity
স্যার আপনিও গায়বি নামাজ পড়ার জন্য নিজেকে তৈরী করে নেন।,0,celebrity
নিজের শহীদ বাবাকেও অসম্মান করলেন স্যার!,0,celebrity
আমার চোখ খুলে দিলেন,0,celebrity
"আপনারা ফন্ট লাইনে আছেন, আপনাদের ডাকে অনেকে ছুটে আসে তাই আমি অনুরোধ করছি প্রশ্নপত্র ফাঁসের বিরুদ্ধে পদক্ষেপ নিন। জেলায় জেলায় জনমত গড়ে তুলুন। আমরা যুব সমাজ আপনার পাশে আছি।",0,celebrity
"Sorry sir..আপনি যে আ:লীগের দালাল তা আগে জানা ছিলনা,আজকের এই অবস্তার জন্য দায় কে আপনি কি বলতে পারেন?",0,celebrity
আপনার পরকাল থেকে পাঠানো পোস্টের উপর হড হড করে বমি করে দিলাম,0,celebrity
স্যার অন্নেক আগেই পটল তুলিয়াছেন ! তামিল মুভীর মত পূনজন্ম নিয়ে আবার এসেছেন  সিলেটে ভোট দিতে !! এবার একখানা ইসটেটাস পোস্টাইয়া তিনি মৃত্যুর এই উপত্যকা দিয়া চিরতরে নরকে প্রবেশ করিবেন !! টাঊট !!,0,celebrity
"""রাজাকার""শব্দটিকে জাতীয় সংসদ থেকে আইন করে অবৈধ ঘোষনা করা হোক।এবং বাংলা অভিধান থেকে বাতিল করা হোক।#দৈনিক_ইত্তেফাক😊যাতে বাংলার মাটিতে আর কোন রাজাকার জন্মাতে না পারে।",0,celebrity
"জানি, আপনি ফেসবুকের কমেন্ট পড়েন না তবুও যারা ফেসবুক চালান তারা অন্তত উপলব্ধি করবেন। আপনি অনেক শিক্ষিত, জ্ঞানী, পন্ডিত, বিজ্ঞজন। আপনার ভুল ধরা আমাদের কম্য নয়। কিন্তু যেটা ঠিক বুঝতে পারিনি তা হল ""নারী পুরুষ সমতা""। আপনি কি সমতা চান নাকি সাম্য? "" সমতা"" বললে তো সংসদে সংরক্ষিত আসন থাকবেনা, বাসে কোন ""মহিলা"" লেখা কোন আসন থাকবেনা, চাকুরীতে কোন মহিলা কোটা থাকবেনা এমনকি পুরুষের জন্য নির্মিত দাড়িয়ে প্রসাব করার কমোড তাদেরকেও ব্যবহার করতে হবে। বিষয়টা ভেবে দেখবেন।",0,celebrity
"বাস ট্রাকের ড্রাইভারগুলো আপনাকে খুব অনুসরণ করে,  মানুষ মেরেই গর্তে ঢুকে যায়,  পুলিশ খুঁজে পায়না।",0,celebrity
"আরে আরে, এসব কি? লাইনে দাড়ান, না,না, হবে না, ধাক্কাধাক্কি করবেন না, একটার বেশি বাশ দেয়া যাবে না। সবাই অনেক দিন ধরে অপেক্ষা করছে। একটা করে ঢুকিয়ে দিয়েই বা দিক দিয়ে বেরিয়ে যান। পরেরজনকে সুযোগ দিন।",0,celebrity
"কেউ উনার সম্পকে ভাল কিছু লিখেন,না হলে বেচারা ওপারে গিয়েও শান্তি পাবে না",0,celebrity
"কয়দিন নয় স্যার , অনেকদিন......",0,celebrity
"সবাই দেখি আমারমত কমেন্ট পড়তে আসছে, তাহলে কমেন্টটা লিখবে কে- #সিফাত_কাকু????",0,celebrity
তারাতারি ভাল হয়ে উঠুন স্যার। আপনাকে খুব তারাতারি ভাল হতে হবে স্যার,0,celebrity
আপনি নিজেও রাজাকার।   যুদ্ধ না করে নিজে পালিয়েছিলেন কেন?,0,celebrity
সম্পুর্ণ লেখার কোথাও মুক্তিযুদ্ধের চেতনা না থাকায় খুব কস্ট পেলাম। (২),0,celebrity
"মুশফিকুর রহমান sobai jokhon mara ditese status maira,dekhtese kisu na koile pore boi bikri hobena tokhon mukh futeche bacchar :v",0,celebrity
"অনেকদিন পর আপনার একটা ভাল লেখা পড়লাম। সরকার যেন এই কাজটা সম্পন্ন করতে পারে, সে কামনা করছি।",0,celebrity
পাগল কোথাকার,0,celebrity
"হে শিক্ষার্থীরা! তোমাদের আদর্শ শিক্ষক এখনো বেঁচে আছেন, তোমরা কাইলকা হেতেরে বাঁশানোর জন্য রেডি হয়ে যাও৷ Siam Araf",0,celebrity
"""গরুর মাংশের মুখোশের মালিক"" =========================  হোটেলে খেয়ে তেহারি বিপদে নাহি পড়ি।  অগোচরে রয় কুকুরকে গরু বলার ভয়ংকর ফাঁক! কুকুরের মুখোশে ঢাকা কিছু হোটেল মালিকের হাক।  যথাযথ কিছু লোক  গরুর মাংসের মুখোশের  মালিকের গলায় ঘন্টা পড়াতে পারে। এই তাহারা এই ঘন্টা রাখে আঁধারে।  এর থেকে সরবরাহকদেরও কারো রেহাই নেই। কুকুরের মাংশ খাচ্ছে তারা আপন মনেই।",0,celebrity
ইনিয়ে বিনিয়ে সমর্থনকে সমর্থন বলে না। পরিস্থিতি এমনটা চায় না। চায় স্বল্প বাক্যে জাস্টিজ। ছাত্রদের সাথে জনপথে নেমে আসুন।,0,celebrity
"স্যার এর লেখার পর, ওনার কমেন্টস এর উত্তর দিতে হবে। ওনি ওনার মতো করে বলে যান,,,,,, এই বিষয়ে একটা ইভেন্ট খোলা যায় যে, লিখলে অবশ্যই কমেন্টস পরতে হবে।",0,celebrity
আপনার মত ভন্ডের মুখোশ এখন সবার কাছেই উন্মুক্ত। কমেন্টগুলি পড়লেই বুঝতে পারবেন,0,celebrity
এতবড় লেখা কেউ পরে রে ছাগল?? আর আপনি  যে চকিরতলা সেক্টরের মুক্তিযোদ্ধা তা কিন্তু সবাই যানে,0,celebrity
"ওমা এডা কেডা জাফর ষাঁড় নাকি,,, ষাঁড়েকি ঢাকা থেকে সিলেট যাবার সময় ভুতের থাপ্পড় খাইয়া এতদিন অজ্ঞাত অবস্থায় ছিলেন।!!!  নিষ্চই কোনো ওজা এতোদিন আপনাকে ঝার - ফুক দিয়ে বালা করছে।।। আপনি তাই অজ্ঞাত অবস্থা থেকে জাগিয়া,,,, কারো হরহর গরগর বমির গন্ধ পাইয়া।।। সম্রাট সাজাহান ও নবাব সিরাজউদ্দৌলার থেকে বড় ইতিহাস লেখে রাতের ঘুম হারাম করার জন্য ফেসবুকে দিছেন।।।",0,celebrity
যারা কমেন্ট করেন তারা হয়তো জানেন না জাফর ইকবাল স্যার এই সব পাছে লোকে কি বলে তা নিয়ে মোটেও ভাবেন না।,0,celebrity
আমি লেখাটি পত্রিকায় ইতিি পূর্বে পড়েছি ও সংরক্ষন করেছি । ওনার প্রস্তাবের সাথে সর্বতভাবে একমত ।,0,celebrity
রাজাকারের মেজো নাতী,0,celebrity
লিঙ্গ হবে ??🖕🖕 ভরে দিতাম।🦁🦁,0,celebrity
এই লেখাটার জন্য,0,celebrity
উনি(জাফর স্যার) এত্তো ভালো বুঝেন এত্তো চেতনা উনার রক্তে তাহলে একাত্তরে যুদ্ধকালীন সময়ে কুখ্যাত রাজাকার ও শান্তি কমিটির সদস্য শর্ষীনার পিরের আস্তানায় লুকিয়ে ছিলেন কেন? ৭১/৭৫ এ উনি কি করেছেন? নিজে রাজাকারের আস্তানায় লুকিয়ে ছিল আর এখন বড় বড় কথা বলে।,0,celebrity
"অনলি ""জা4 ১বাল""স্যার ইজ হাচা।",0,celebrity
"স্যার আপনিত আবেগি বক্তব্য দিয়ে মানুষের মন জয় করার মিথ্যা চেষ্টা করলেন,আপনার কি করা উচিৎ সেটা কি মন্ত্রী পুলিশ এ্রর মত আপনাকে ও চোখে আঙ্গুল দিয়ে দেখিয়ে দিতে হবে...।",0,celebrity
sir তাহলে কি আমাদের জাতিটা নষ্ট হয়ে যাবে????স্যার আমরা কি করতে পারি!,0,celebrity
৭১ এ ও গর্তে লুকাই ছিলেন ।১৮ তে ও না হয় থাকতেন ।এতো ফর্মালিটি করে পোস্ট না দিলেও হইতো।মুক্তিযোদ্ধারা যেমন চেতনাবাদীদের জন্য বইসা থাকে নাই তেমনি ছাত্ররা ও বইসা থাকে নাই।,0,celebrity
আজ জাফর ইকবাল স্যার বেঁচে থাকলে ছাত্রদের এতো ভোগান্তি হতো না। ওপারে ভাল থাকুন।,0,celebrity
"জাফর ইকবল স্যার যে বিষয়টা সবাইকে বোঝাতে চাচ্ছে সে দিকে কেউ যেতে চাচ্ছেনা বিষয়টা হল এই।তিনি সবাইকে বোঝাতে চাচ্ছেন যে রাজাকার শব্দটার সাথে  নির্যাতন,ধর্ষণ,অগ্নিসংযোগ সহ যত প্রকার অপরাধ আছে সবই জড়িয়ে আছে।তাই একজন বাংলাদেশী হিসাবে  কোন তরুন তরুনীরই উচিত নয় এই শব্দটা ব্যবহার করে নিজেকে ট্যাগ দেওয়া। এখন যদি মতিয়া চৌধুরি বলে যে মুক্তিযোদ্ধাদের সন্তানরা চাকরি করবে না তো কি ধর্ষকরা চাকরি করবে??? এর উত্তরে কি নিজের  গায়ে #আমি_ধর্ষক এটা লাগাতে পারবে কোন তরুণ?? পারবেনা। কেন পারবেনা?  কারন ধর্ষণের ভয়াবহতা বর্তমান প্রজন্ম দেখেছে,তাই পারবেনা।ঠিক তেমনি জাফর ইকবল স্যার রাজাকারদের স্বচক্ষে দেখেছেন বলেই রাজাকার শব্দটার প্রতি তার ঘৃণা মিশ্রিত আছে।তাকে অবলিলায় দোষ দেওয়া যায়না। গায়ে রাজাকার লেখাতে সুধু জাফর স্যার একা নয়, প্রতিটি মুক্তিযোদ্ধাই কষ্ট পেয়েছেন, কেউ প্রকাশ করেছেন কেউ করেননি।",0,celebrity
স্যারের পেইজ লাইকাররা দেখি সবাই স্যারের শত্রু। আপনারা যখন স্যারকে এত ঘৃনা করেন তো স্যারের লেখা পড়েন কেনো পেজ থেকে সসম্মানে বাহির হয়ে যান এত পেচাল পারেন কেন।,0,celebrity
আপনিও পঁচে গেলেন!  😂😂😂 আপনারে স্যার ডাকছিলাম স্যার! 😂,0,celebrity
"ধর্ম সে তো বাহানা স্যার... বাঙ্গালি তো এরা  স্বভাবজাত কারনে কারো সফলতা দেখতে পারেনা। সেটা নিজের ভাই হোক বা বাপ হোক বা প্রিয় বন্ধু যেই হোক। হুমায়ন আহমেদ তার নিজের দেশে সবচেয়ে বেশি নিন্দিত, সাকিব আল হাসান এর সবচেয়ে বেশি নিম্দুক এই দেশে... এদেশের বেশিরভাগ মানুষ পড়াশোনা করে নকল করে স্বভাব টা এতই খারাপ হয়েছে যে ধর্মটাও শিখে ওয়াজ শুনে...  get well soon",0,celebrity
"কমেন্টে আসছিলাম বমি করতে, এত বমি ভিড়ে আমার বমি আসছেনা!!!#",0,celebrity
দালাল👿,0,celebrity
আপনার সুন্দর মন আর চোখ দিয়ে পৃথিবীটা আরও অনেকদিন দেখতে হবে আপনাকে।,0,celebrity
এইসব বেয়াদবদের স্যার বলে ডাকাও বিয়াদবি।,0,celebrity
"Sayedur Rahman কিউবার নিপীড়িত জনগণের সাহায্যার্থে ফান্ড গঠনের লক্ষ্যে এক রাজনৈতিক পার্টির কিছু কর্মী কলকাতার রাজাবাজারে বাসের ভিতর চাঁদা সংগ্রহ করছিলো৷ বাসের যাত্রীরা যার যার সামর্থ্য অনুযায়ী দু'হাত ভরে চাঁদা দিচ্ছিলো৷ কিন্তু এক বৃদ্ধ বেঁকে বসলেন৷ পার্টির কর্মীরা তাঁর সামনে চাঁদার বাক্সটি মেলে ধরতেই তিনি বললেন, ""কলকাতায় বসে আমি কিউবার জন্য চাঁদা দেব কেন? সেখানে কি হয়েছে?"" রাজনৈতিক কর্মীটি তখন অবাক হয়ে বললো, ""সে কি! আপনি জানেন না? মার্কিন সম্রাজ্যবাদের বর্বর পাশবশক্তি কিউবার উপর কি নগ্ন আক্রমণ চালাচ্ছে, তা শোনেন নি? "" বৃদ্ধ গম্ভীরভাবে বললেন, "" আরে বাবা! এ আর নতুন কি? পাশবশক্তি যার আছে সেতো দূর্বলের উপর পৈশাচিক আক্রমণ করবেই! বানতলায় দেখোনি?"" লজ্জায় ছেলেগুলো মাথা নত করে বাস থেকে নেমে পড়লো৷ কারন এর কিছুদিন পূর্বেই বানতলায় একটা মেয়ে ধর্ষণের শিকার হয়েছিলো, অনেকের ঘর বাড়ি জ্বালিয়ে দেওয়া হয়েছিলো৷ ছেলেগুলো যে পার্টির সমর্থক তাদের পার্টি ছিলো সেখানকার ক্ষমতায়৷ দুই লক্ষ মা-বোনকে ধর্ষণের জন্য আমরা পাকিস্তানীদের ঘৃণা করি৷ স্বাধীন বাংলাদেশে মোট কত লক্ষ নারী ধর্ষণের শিকার হয়েছে তার সঠিক কোন পরিসংখ্যন না থাকলেও; বাংলাদেশ পুলিশ সদর দফতরের অপরাধ পরিসংখ্যান অনুযায়ী, গত চার বছরে সারা দেশে ধর্ষণের শিকার হয়েছেন মোট ১২ হাজার ৯৭১ জন৷ ইংরেজী বছরের প্রথম দিনটা শুরু হয়েছে, নোয়াখালীর সুবর্ণচরেরে চার সন্তানের জননীকে ধর্ষণের মাধ্যমে৷ এ আর নতুন কি! যার পুংদন্ড আছে সে তো ধর্ষণ করবেই৷ নৃপুংসুকদের দন্ডগুলো জেগে উঠুক৷ তারা পরিণত হোক ধর্ষকে৷ আগামী দিনগুলো হোক শুধুই ধর্ষকদের৷ এই প্রত্যাশায়, ""হ্যাপি নিউ ইয়ার""",0,celebrity
"অান্নে কি কবরের তোন উডি নি লেখছেন, অাই মনে কইচ্ছি অাননে জাতীয় বুবির লগে চান্দে চলি গেছেন, ওমা ওন দেন খইল্লা মাছের মত ভেটকি দি নুরানী খোমা দেখাই অাবার ডুব দিছেন।",0,celebrity
"স্যারের বাসাটা আবার মেয়েদের ""হোস্টেলের"" কাছাকাছি!!! বুঝতে হবে মেয়েদের প্রতি রয়েছে স্যারের অবাধ ভালবাসা...",0,celebrity
স্যার যে দেশে আমি রাজাকার বলে নিজেকে (গরববতী) বানাতে পারে সে মুক্তিযোদ্ধার চেতনাধারী হবে কেমনে বিশ্বাষ করেন। খুব দুঃখের সাথে বলছি আপনার পোস্টের কম্মেন্ট গুলো না পড়লে আমি খুব খুশী হই যদি পড়ে থাকেন খুব লজ্জিত বোধ করছি। ৫ হাজারের উপরে কম্মেন্ট দেখে অবাকও হয়নি।পাকি বীজ বাংলাদেশে রয়ে গেছে যার বাস্তব উদাহারন ১৯৭১ মুষ্টি কয়েক মুক্তিযোদ্ধা ছিল।যার কারনে আমি মুক্তিযোদ্ধার সন্তানের বদলে আমি রাজাকারের সংখ্যাটা বেশি।খুব লজ্জা লাগে পাকি দালালে ভরা আমার সোনার বাংলাদেশ।আবার যদি যুদ্ধ হয় তাহলে ঠিকই রাজাকারের বাচ্চা রাজাকার ই হবে তাই এদেশে বাচঁতে হলে রাজাকারকে রাজাকার বলতে পারবেন না দালাল বলতে হবে।আপনার সম্মান আপনি রাজাকারের বাচ্চা থেকে না ফেলেও মুক্তিযোদ্ধার সন্তান থেকে পাবেন। আশাকরি দুঃখ কিছুটা লাগব হবে।স্যার সত্যকে সত্য বলতে পারাটাও একটা যুদ্ধ।তাই আপনার যুদ্ধটা যেন কলম দ্বারা অব্যাহত থাকে।কারো ভয়ে যেন কাবু না হন আপনার দেখা গল্পগুলো আরও বেশী বেশী জানতে শুনতে চাই। ভালো থাকবেন। আল্লাহ আপনার সহায় হোন।,0,celebrity
ঠ্রস ঠ্রস করে পাছার চামড়ায় বাড়ি দিতে হবে,0,celebrity
এই কম্যান্ড গুল পরে বুঝতে পারলাম এখানে বেশিরভাগ মানুষের অকারণে বমি করার রোগ আছে। আশা করি তাদের রোগ খুব তারাতারি ভালো হোয়ে যাবে,0,celebrity
"নাথিং টু সে স্যার। নিজ চোখে তরুণ প্রজন্মের দারুণ অধঃপতন দেখতে পাচ্ছি।আমরা ছিলাম,আছি,থাকব। ক্যারি অন স্যার।",0,celebrity
"ভোট দিতে পারবে কি না তা জনগনের কোন গ্যারান্টি নাই।  গণতন্ত্র হরণ, বাক স্বাধীনতা হরণ,  দুর্নীতি বাজ,  মানি লন্ড্রি, শেয়াবাজার দুর্নীতি,  হলমার্ক ক্যালেনকারি, টেন্ডারবাজি সহ সব কিছু বাদ নির্বাচনী ইসতেহার হয় কি করে.....",0,celebrity
"স্যার আপনার মূল্য ওরা বুঝে না, আর কোন দিন ও বুঝবে না,আপনি জাতির বিবেক আপানার মত মানুষ কে ওরা কোন দিন ও মারতে পারবে না।আপনি ছিলেন,আছেন থাকবেন কোটি কোটি মানুষের মন জুড়ে।",0,celebrity
আমি একজন  জেএসসি পরিক্ষারথীর মা।সত্য বলতে আসলেই ওদের জিবনে  আনন্দ নেই।শুধু পড়ালেখা।কিন্তু তাদের   coaching center  নিয়ে আর কষ্ট না দিতে সব মাবাবা কে অনুরোধ করছি।,0,celebrity
"কেমন আছেন স্যার? গতকাল থেকে মনটা খুব খারাপ ছিলো,এখন আপনি পোস্ট দিয়েছেন,আর হাগার হাগার মানুষ কমেন্ট করবে,আর সেই কমেন্টগুলা দেখে আমার মন ভালো হয়ে যাবে। ধন্যবাদ স্যার,মানবতাকে আজোও বাঁচিয়ে রাখার জন্য।",0,celebrity
অবশেষে শিক্ষামন্ত্রী উদ্দ্যোগ নিলেন পাবলিক পরীক্ষা চলাকালীন দিনগুলোতে ফেসবুক বন্ধ করে দিবেন।   প্রশ্নটা ফাস হয় প্রধানতো ফেসবুক পেজ থেকেই। ফেসবুক বন্ধ করে দিলে  প্রশ্নপত্র ফাস পুরোপুরি বন্ধ করা না গেলেও আমি আশাবাদি কিছুটা হলেও রক্ষা  পাবে।  তাছাড়া পরীক্ষা চলাকালীন সময়গুলোতে যদি ফেসবুক বন্ধ থাকে তবে শিক্ষার্থীরা পড়ারও সুযোগ পাবে।   তবে যারা পরীক্ষার্থী না তারা হয়তো আন্দোলন টান্দোলনে নামতে পারে। তবে  কোমলমতি শিক্ষার্থীদের কথা বিবেচনা করে অবশ্যই আপাত: এ উদ্দ্যোগটাকে স্বাগত  জানানো দরকার।  শুধু যে ফেসবুক থেকেই প্রশ্ন আউট হয় তা কিন্তু না।  বিভিন্ন মাধ্যমে প্রশ্ন আউট হতে পারে। তবে আমজনতা প্রধানতো ফেসবুক থেকেই  প্রশ্নপত্র পেয়ে থাকে।   সরকার বা প্রশাসনের একার পক্ষে এ কলংক নিরূপন করা সম্ভব না। প্রয়োজন সবার সহযোগিতা।  শিক্ষামন্ত্রীর এ উদ্দ্যোগকে স্বাগত জানাইলাম।,0,celebrity
"স্যার, নিজের সম্মান ধরে রাখতে শিখুন। 🙂",0,celebrity
"যারা শুধু এই  বাংলাদেশের নারী বিষয়ক  পোস্টটি পড়েছে  তারা লাভ রিয়্যাক্ট দিবে,,, আর যারা বাংলাদেশের নারীদের সার্বিক পরিস্থিতি সম্পর্কএ অবগত, তারা এখানে হাহা দিতে বাধ্য,,,,,",0,celebrity
অাপনার মত garbage এর সমর্থন কোটা অান্দোলনকারীরা চায় নি।,0,celebrity
"বাচ্চাটাকে সন্ত্রাসী মনে করে চেক করা হয়না, কোন সন্ত্রাসী বাচ্চাটার আড়ালে বেআইনি কিছু বহন করে কিনা তা যাচাই করতেই চেক করা হয়। বিষয়টি আপনি জানেননা তা নয়,  না জানার ভান করেছেন।  আপনি পেট্রোল বোমা বোঝেন গায়েবী মামলা বোঝেননা, ক্রসফায়ার বোঝেননা, গুম বোঝেননা - এই ভান করার কারণেই বিরক্ত মানুষগুলো আপনার লেখায় উল্টোপাল্টা মন্তব্য করে।   মানুষ সব জায়গায় বিচারহীনতায় থাকতে থাকতে ত্যাক্ত-বিরক্ত। সেজন্য একটুতেই তাদের মুখ খারাপ হয়ে যায়। আপনার এই ভান করা লেখা পড়লেও তাই তাদের মুখ খারাপ হয়ে ওঠে- যেটা ঠিক না। তবে এগুলো আপনার হাতের কামাই, কী আর করবেন।",0,celebrity
" স্যার, পড়ার চাপে আপনার লেখাটা পড়তে পারলাম না।কিন্তু একটা কথা জিজ্ঞেস করতে চাই, রাজনৈতিক উদ্দেশ্য হাসিল করতে যেয়ে যে,গণহারে ভাল রেজাল্ট দেওয়া হচ্ছে তা দ্বারা কি দেশের কল্যাণ সম্ভব বলে আপনি মনে করেন? ",0,celebrity
"আমি কিছু জানিনা, জানতে চাই, জানার আগে বিশাল লেখা উপহার দিতে চাই। কি চমৎকার ;)",0,celebrity
"পোলাপাইনে সব পারে 😀 হাসতে হাসতে আমি গেলাম, আর কমেন্টস পড়তে পারতেছিনা। আবার যত পড়ি আরো পড়তে ইচ্ছা করে।",0,celebrity
আপনি দুষ্টুদের উপর হড় হড় করে বমি করে দিচ্ছেন না কেনো??,0,celebrity
আপনি  তাহলে  সুস্থ  এখন।,0,celebrity
"অসাধারন সত্য। বিশ্ববিদ্যালয়ের প্রমোশনের নিয়ম খুবই উদার, বয়স হলেই লেকচাররা দেখতে দেখতে প্রফেসর হয়ে যায়!:-V ",0,celebrity
আস্তা দালাল,0,celebrity
"পোষ্ট পড়ার দরকার নাই, খালি কমেন্টগুলা পড়😂😂😂😂 Ôdïsshø Bälíkà",0,celebrity
"এতকিছু হবার পরেও যদি আপনি কিছুই না জেনে থাকেন তাহলে আমি ছোট মুখে হলেও বলবো,  স্যার আপনার লেখাটা ডিলেট করেন করা উচিত। যে ব্যাপারে আপনি জানেননা সে ব্যাপারে আপনার লেখার অধীকার বা দরকার কোনটাই নেই।  শহিদুল আলম স্যারকে ধরে নিয়েছে শুধু এটুকু জেনে তার পক্ষে বা বিপক্ষে লেখার অধীকারটুকু আপনি অর্জন করেননি। আর ৩য় পক্ষের ব্যাপারে প্রশ্নটা আপনার একেবারেই পিঠ বাচানো টাইপ প্রশ্ন আর আমার বিশ্বাস এই একটা লাইনেই আপনার পরিচয়টা আবারো ক্লিয়ার করার জন্য লিখছেন।",0,celebrity
উনি নাস্তিক এই কথার প্রচলন কে করল!!,0,celebrity
আবোলতাবোল পরিখা গুলো দিয়ে কি আমরা আমাদের ছেলে মেয়েদের জটিল করে তুলছি নাহ ??,0,celebrity
বস্তা পচা কথা আপনার মতো মানুষের মুখে। আফসোছ....,0,celebrity
এখন  কেনো লিখতে পাড়বেন না স্যার। আপনি ও কি ভয়ে আছেন??,0,celebrity
"মদ খাবো শুধু,,,,,আর কিছু না",0,celebrity
"আন্দোলন করে কোন লাভ নেয়ি, কারন যেখানে মিথ্যা দিয়ে দেশ ঢাকা সেখানে আন্দোলন করে কি হবে, তবে খুব কষ্ট পাচ্ছি এই ভেবে যে কষ্ট করে কেন বাচ্ছাদের  পড়াতে  পড়াতে মেরে ফেলছি না পড়ালেই পারি, জানিত পরীক্ষার সময় প্রশ্ন ত পাবই..............................দিক্কার জানায়ি এই সরকারকে.........",0,celebrity
ধন্যবাদ স্যার।,0,celebrity
অাপনার লেখা পড়তে অাসছি না কমেন্ট  পড়তে অাসছি!,0,celebrity
জাফর ইকবাল কি সত্যি সত্যি বেচে আছেন???,0,celebrity
পোস্ট টা দেয়ার পর একটা হজমশক্তি বৃদ্ধিকারক ট্যাবলেট খেয়ে নিয়েছিলেন ত? 😒,0,celebrity
স্যার আরো কিছু মহিলাদের মন জয় করে নিলেন।,0,celebrity
"Habibur Rahman Jewel, you are right bro. তবে আমার খালাকে আমি বুঝাতে পারিনি, আমার খালাত বোন ঐ ফাঁস হওয়া প্রশনপএ দিয়ে পরিক্ষা দিয়েছে! উনার কথা ছিল, সবাই এটা করছে! তো আমরা করলেই দোষ!! :-(",0,celebrity
"হায় হায় আমি যে, আপনার মৃত্যুতে শোকাহত হয়ে স্ট্যাটাস দিছিলাম। :-P  এখন কি সেটা কেটে ফেলতে হবে?  নাকি আপনি আবার মরে যাবেন? :-D",0,celebrity
"স্যার হলিঊড তো হইলো, এবার একটা তামিল মুভি কপি কইরা বই লেখেন। জাতি উরাধুরা ফাইটিং দেখতে চায়  :D",0,celebrity
"স্যার,জীবনে অনেক বার ইতিহাসে   ""রাজাকার""  শব্দটা শুনছি কিন্তু আজ স্বঃচোক্ষে দেখলাম ।একটা দুটো না!৩ হাজার।।।।। ধন্যবাদ স্যার",0,celebrity
you are great.,0,celebrity
ইশতেহারঃ (১৯৯১- ১৯৯৬) শাসনামলে বিএনপি-জামায়াত জোট সরকার পূরণ করছে ৩৩% (১৯৯৬-২০০১) শাসনামলে অাওয়ামীলীগ সরকার পূরণ করছে ৫২% (২০০১-২০০৫) শাসনামলে বিএনপি-জামায়াত জোট সরকার পূরণ করছে ২৪% (২০০৮-২০১৪) শাসনামলে শাসনামলে মহাজোট সরকার পূরণ করছে ৬৭% (২০১৪-২০১৮) শাসনামলে অাওয়ামীলীগ সরকার পূরণ করছে ৯২% সূত্রঃ বিবিসি বাংলা।  ভোট কাকে দিবেন সিদ্ধান্ত আপনার।,0,celebrity
আপনি মতামত দেবার আগে শহীদুল সাহেবের ইন্টারভিউ দেখে নেওয়া উচিৎ ছিল।,0,celebrity
জিয়াউর রহমান ছিলেন একজন সেক্টর কমান্ডার মুক্তিযুদ্ধের আর আপনি ছিলেন গর্তে লুকিয়ে থাকা একজন কাপুরুষ। একজন কাপুরুষ কখনো মুক্তিযুদ্ধের সেক্টর কমান্ডারকে শ্রদ্ধা করতে জানবে  না এটাই স্বাভাবিক।   আজকের স্কুলে পড়ুয়া ক্লাস ৮-৯ এর ছেলেরা আপনাকে নিয়ে মজা করে আর সেই বয়সে আমি আপনার আমি তপু পড়ে কেঁদেছিলাম(দুঃখের বিষয় আমি তপু ইংরেজি একটা সাহিত্যের নকল)। আপনার এত অধঃপতন হল কেন কখনো কি ভেবে দেখেছেন?,0,celebrity
আরো সুন্দর গালি আমি জানি রাজাকারদের জন্য তা হলো মাদার চোদ। জাফর ইকবাল তাই। তাছারা ও রাজাকারের বাচ্চার। কোটা সংস্কার আন্দোলনে রাস্তাঘাট অচল করে দিয়েছে বলছে! সাহাবাগ আন্দোলনে কি হয়েছিল?,0,celebrity
আপনি কি নিয়মিত অনলাইনের স্যারের লেখা পড়েরনি? আপনি না যেনে এইরকম লেখা উচিত হয়নি। Mr. Sowkat,0,celebrity
"আবু বকরকে মনে পড়ে ? ঐযে দিনমজুরের ছেলে ! ঢাকা বিশ্ববিদ্যালয়ের ইসলামের ইতিহাস ও সংস্কৃতি বিভাগের ৩য় বর্ষের ছাত্র ... ছাত্রলীগের গুলিতে খুন হবার আগে যার সিজিপিএ ছিল রেকর্ড ৩.৭৫ ! রেজাল্ট বের হবার আগেই সে খুন হয় , রেজাল্ট বের হবার পরে দেখা গেল - মৃত আবুবকরই বরাবরের মত প্রথমস্থান অর্জন করেছিল । তার হত্যাকারী ছাত্রলীগের নেতারা কিন্তু ঠিকই ২০১৭ সালে আদালতের রায়ে খালাস পেয়ে বের হয়ে গেছে । আবু বকরকে কেউ খুন করেনি ! . তনুকে মনে আছে ? অথবা বগুড়ার সেই মা আর মেয়ের কথা - যাদের তুলে নিয়ে ধর্ষণ করেছিলো তুফান লীগ?  . পটুয়াখালীর সেই হিন্দু মা আর মেয়ের কথা , যাদের তুলে নিয়ে ট্রলারে ধর্ষণ করেছিল ৬ সোনার ছেলের দল ? অথবা বুশরা নামের মেয়েটি ... যাকে ধর্ষন করে হত্যা করা হয়েছিলো ? ফাঁসির রায় পাওয়া সব নেতারাও কিন্তু খালাস পেয়ে বের হয়ে গেছে। অথবা , গাজীপুরের সেই হতদরিদ্র বাবা আর মেয়েটির কথা , যে শিশু মেয়েটির ধর্ষনের বিচার না পেয়ে অসহায় বাবা মেয়েটিকে নিয়ে রেলগাড়ির নিচে শুয়ে পড়ে আত্মহত্যা করেছিল ? মনে পড়ে ? . মনে আছে পহেলা বৈশাখে মেয়েদের গণযৌননির্যাতন ? সকল ভিডিও ফুটেজ আর ইমেজ ছিল ...কিন্তু কারা অপকর্ম করেছিল , তার কি বিচার হয়েছে ? . মনে আছে ৭ ই মার্চের সমাবেশ উপলক্ষে রাজধানীর রাস্তায় রাস্তায় সোনার ছেলেদের দ্বারা মেয়েদের যৌননির্যাতন ? হয়রানি ? . অথবা শাজাহান খানের শ্রমিকদের দ্বারা মেয়েদের শরীরে মাখানো কালি ? প্রতিনিয়ত বাসের ভেতর ধর্ষন ? কোন সুবিচার পেয়েছেন ? . মনে পড়ে , হলের ভেতর নিয়মিত ছাত্রীনির্যাতনের প্রতিবাদ করতে গিয়ে উলটো বহিষ্কৃত হতে হয়েছিল আপনার সহপাঠিনীদের ? . অথবা চাকরির দাবীতে আপনার ও আপনার সহপাঠীর উপর নেমে আসা নির্যাতন, আপনার সহপাঠিনীর বুকের ওড়না ছিড়ে ফেলা ...অথবা সংবেদনশীল অঙ্গে পশুদের হাত ...মনে পড়ে ? . অথবা নিরাপদ সড়কের দাবীতে রাস্তায় নামা আপনার ছোট ভাই বোনদের উপর নেমে আসা অত্যাচার ? . ৩০ ডিসেম্বর আপনি সব ভুলে বাসায় একদিনের আরামপ্রদ ছুটি কাটাতে পারেন এবং ভবিষ্যত ৫ বছর রাস্তাঘাটে-শিক্ষাপ্রতিষ্ঠানে নিজেদের এবং নিজের আপনজনদের হয়রানির শিকার হতে দেখতে পারেন , নিশ্চিত থাকুন - কোন বিচার পাবেন না । . অথবা ৩০ ডিসেম্বর আপনি কষ্ট করে ভোট কেন্দ্রে গিয়ে সকল অবিচারের পাওনা সুবিচার আদায় করতে পারেন । পছন্দ আপনার । কারন ভবিষ্যতটাও আপনার । হয় ভুগবেন আপনি । না হয় ওদের ভোগাবেন আপনি ।",0,celebrity
পরিবহন সন্ত্রাস রুখে দিতে ছাত্রদের আন্দোলনটি দরকার ছিলো! এই উছিলায় পরিবহন খাতকে সংস্কার করা যেত।উপকৃত হতো সব বাংলাদেশী মানুষ।তবে গডফাদারকে স্বপদে বহাল রাখলে সাময়িক আন্দোলন বন্ধ হলেও আবারও মানুষকে পরিবহন নৈরাজ্যে ভোগতে হবে।কারণ আমরা দেখেছি তারেক মাসুদ ও মিশুক মনির মারা যাওয়ার পর সরকারকে বৃদ্ধাঙগুলী দেখিয়ে দুই দিন দেশ অচল করে রেখেছিল কথিত এই গডফাদার!,0,celebrity
"মদ খা,  মদ না খাইলে এমন পোস্ট দিতে পারবি না 😂",0,celebrity
কোটাবিরোধী নয় কোটা সংস্কার।  স্যারের কোথাও ভুল হচ্ছে :),0,celebrity
"Psc একটা আজুরে বেপার,খুব বাজে এর কি মূল্য আছে একমাএ JSC,JDC,",0,celebrity
এই যে কমেন্টকারী ভাইয়েরা আপনাদের কি বাচ্চা পেটে এই কারণে বমি আসে ?????????????????????????????,0,celebrity
"আপনি কি লিখলেন সেটা তো নিজেই জানেন না। অগনতান্ত্রিক লেখা। একবার কমপক্ষে কিছু গ্রাম ঘুরে আসুন না!  তবেই বুঝবেন এ দেশের মানুষেরা কি চায়?  সত্যিই, অবাক হচ্ছি, আপনাদের মতো ব্যক্তিরা কি করে গনতন্ত্রের বুলি আউড়ান!!!  বিভাজনের রাজনীতি কি করে দেশে শান্তি আনবে দেশে! যদি নাই বোঝেন কিছু, তবে লিখেন কেন?  এক পয়সাকড়ি মূল্য নেই আপনাদের মত মানুষের লেখার। নিজেকে সংশোধন করুন। সম্ভবত ভালোই হবে।",0,celebrity
"সবাই বলতেছিলো মাদারটোস্ট মইরা গেছে, কিন্তু আমি বিশ্বাস করিনাই। কারন আমি জানতাম যে এই মাদারটোস্ট মানুশ হয়তে সাফায়েত কাককুর কাছে গেছে :D হ্যা যা ভেবেছিলাম তাই, আজকে সদ্য ছাড়া পেয়ে অমানুসের বাচ্ছা হয়ে মানুসের মাঝে পোস্ট করেছেন। আল্লাহ ওপারে উনাকে হেদায়েত দান করুক :D আমিন  #আমিন না লিখে কেউ যাবেন না আসা করি",0,celebrity
আমার মনে হয় কিছু দিনের মধ্যে বাংলাদেশে  ফেসবুক বন্ধ করে দিবে। সো যারা বন্ধ আবস্থায় ফেসবুক ব্যাবহার করতে চান। তারা বিপিএন রেডি রাখেন। জয় বাংলা। share it...,0,celebrity
রাজাকারের বাচ্চারা ষ্যাড়কে  যা তা বলছে এদের উচিত শিক্ষা দেয়া উচিত!,0,celebrity
আমি রাগ করে মাঝে মাঝে একটি কথা বলি এই দেশ এর সবার মানুষিকতা কথনও বদলানো যাবে না..................,0,celebrity
"১. সংসদে দাঁড়িয়ে একজন মন্ত্রী কিভাবে দেশের হাজার হাজার শিক্ষার্থীকে রাজাকার বলে বা বলাটা কতটুকু গ্রহনযোগ্য তা ব্যাখ্যা করবেন।  ২. শাহবাগে অান্দোলন অাজকে নতুন না। ২০১৩ তে নিজের বুদ্ধি বয়সের সবচেয়ে বড় জনসমাগম দেখেছি। তখন কি হেলিকপ্টারে মানুষ শাহবাগ পার হত??   ৩. দেশের অর্ধশত বছর বয়সেও যদি অামরা মুক্তিযোদ্ধা পরিবারকে প্রতিষ্ঠিত করতে না পারি তবে সে ব্যর্থতা কাদের?? কথায় কথায় সবকিছুতে মুক্তিযুদ্ধ জড়িয়ে দেয়া বন্ধ করেন।   ৪. বেশ কিছুদিন অান্দোলন চলছিল। তাহলে নম্র থাকা অবস্থায় কর্তৃপক্ষ কেন বিষয়টি অামলে নিল না??   * কোঠা কখনো বাতিল চাওয়া হয়নি,সংস্কার চাওয়া হয়েছিল।  যদি কখনো সময় হয় বিষয়গুলো পরিস্কার করে দিয়ে যাবেন।",0,celebrity
জাফ্র স্যড় আপ্নে ভ্লো কপি ক্রতেজানেন অনেকে সেতাও জানেনা,0,celebrity
আর কত জালাইতাম,0,celebrity
ডাক্তাররা ৫ মিনিটের বিনিময়ে ৫০০০ টাকা নিলে হয় মানব সেবা। আর শিক্ষকেরা ( যারা ডাক্তার বানানোর কারিগর) সারামাস পড়িয়ে  ১০০০ টাকা নিলে হয় বাণিজ্য।,0,celebrity
প্লিজ কেউ কমেন্টে মতিয়া চৌধুরীর লিংক টা দেন! স্যার ঘুমে ছিলেন। স্যারের হিসাব ছিল না!!,0,celebrity
মানভোতা এখনো বেঁচে আছে 😍,0,celebrity
"আপনার জন্য কেন পুড়বো আমরা, ম্যাডাম?সরকার আপনার ক্ষতি করেছে; আপনাকে জনসভা করতে দেয়নি; আপনার বিদ্যুৎ লাইন কেটে দিয়েছে; আপনাকে ক্ষমতায় আসতে দেয়নি গত নির্বাচনে। আরো অনেক কিছু করেছে এই সরকার। এটা কি আমাদের দোষ? আপনি সরকারকে মারুন; আমাদের মারছেন কেন? আমি বা আমরা কেউইতো সরকারকে ওইসব বুদ্ধি দেইনি; তবে কেন মারছেন আমাদের?আপনার আমাকে বোঝাতে হবে কেন আমি পুড়বো? প্রতিদিন আপনার লোকজন আমাকে বার-বি-কিউ করবে, আর আপনি কিছুই বলবেননা তাতো হয়না। ওদের গুলি করতে চাইলে আপনি বাধা দেবেন, অথচ নাশকতার আয়োজনে নিজেও শামিল হবেন— এ কেমন রাজনীতি আপনার!!!",0,celebrity
জ্বী স্যার বুঝে গেছি আসল কাহিনী।  বিএনপি জামায়াতের সময় এমন ধর্ষণ অনেক হয়েছিলো।  মহাজোটের সময় তো মাত্র একটা ঘটনা৷  এটাই তো সারাংশ? 🤣🤣,0,celebrity
আমি স্যারের লেখার কমেন্ট পড়া ভক্ত.. ফেবুতে এর চেয়ে বড় বিনোদন আর কি হতে পারে ফ্রেন্স?!,0,celebrity
"ভাই,কমেন্টগুলো পড়ে যা.... Noyem Uddin KM Nähîd Nuruddin Khan Raj",0,celebrity
আচ্ছা আমরা মুক্তিযোদ্ধা আর রাজাকার থেকে বের হয়ে মানুষ হতে পারিনা ??? হয় ত বা পারব আপনাদের ইন্তেকালের পর !!!!!,0,celebrity
কমেন্ট পরতে আসলাম। ইনফ্যাক্ট মাঝেমাঝেই আসি। এই কমেন্টে হা হা দিয়েন। নোটিফিকেশন পাইলে আবার কমেন্ট পরতে আসব😂😂😂,0,celebrity
"ওনাকে ভুল বোঝানো হয়েছে, প্লিজ কিছু মনে করবেন না।",0,celebrity
আপনার বই গুলা নীলক্ষেত এ বেচে দিসি।  দেশে আরও অনেক ভাল বিজ্ঞান লেখক আছে৷,0,celebrity
মীর জাফর!,0,celebrity
"। যে জাতি শৈশবে অন্যায় করতে শিখে বড় হয়, সেই জাতি দিয়ে আমরা কী করব?",0,celebrity
যারা ভোট চুরি করে ক্ষমতায় বসিয়েছে তাদের কি করার ক্ষমতা রাখে ক্ষমতাধর দল।লজ্জাও এদের কার্যকলাপে লজ্জায় মুখ লুকিয়ে নিছে।এখন ক্ষমতাবানরা হাসতে হাসতে মিথ্যা বলে।নীতির কথা বলে জনগনের সাথে তামাশা করে।,0,celebrity
"প্রথমে বলি উনি কিন্তু ট্যাটু দেখে মুগ্ধ হয়েছেন, আচ্ছা জনাব আপনি কিন্তু বলেন নি কাদের ট্যাটু দেখে মুগ্ধ হয়েছেন উলঙ্গ মেয়েদের নাকি গেই দেখে?  উনি নিজের দেশের এবং নিউইয়র্ক এর এয়ারপোর্ট এর খুব সুনাম করলেন আচ্ছা জনাব এখানে নিজের সুবিধা আছে তাই এত সুনাম না?? আপনাকে চিনে, আপনার সাথে সেলফি তুলে আরো কত কথা। সর্বশেষ বললেন মুক্তিযোদ্ধা নিয়ে, তো জনাব আপনার ভাইয়ের বইয়ে নিজে লিখে গেছেন যে আপনি মুক্তি যোদ্ধার সময় গর্তে লুকিয়ে ছিলেন, অথচ তখন ছিলেন আপনি টগবগে তরুণ। অথচ জাতি আজ একজন ভীরুর কাছ থেকে মুক্তি যোদ্ধের কথা শুনতে হচ্ছে এর চেয়ে লজ্জার আর কি হতে পারে। যাই হোক আপনার এই লেখাটা যে একটা জগাখিচুড়ি লেখা হয়েছে তাতে কোন সন্দেহ নাই।",0,celebrity
"দেশের একটা প্রতিক্রিয়াশীল অংশ আপনাকে অনেক আগে থেকেই দেখতে পারত না কিন্তু যারা আপনাকে ফলো করত, সম্মান করত, আপনার বই পড়ত, আপনাকে আদর্শ মনে করত তাদের কাছে আপনি আজ বিরক্তিকর একটি নাম। এত লিখে কি পেতে চান? সেলিব্রেটি ভাবেন নিজেকে,  পিছনে কারা ছিল তা কি ভাবেন? আপনার আর পাবার কিছুই বাকি নাই সব পেয়েছেন। আর যদি ভাবেন আরো অনেক অনেক খ্যাতি পেতে চান এমন আন্দাকুন্দা লেখনী দিয়ে তবে লিখতেই থাকুন। আপনার জন্য ঘৃণা শুধুই ঘৃণা,,,,,,",0,celebrity
দালালের ভূমিকায় আপনাকে দেখতে পাব কখনো ভাবিনি,0,celebrity
Muhammed Zafar Iqbal এতবড় লেখা যা এক নিশ্বাসে পড়ার জন্য জমাট বাঁধুনি চায়। আর আপনি দক্ষ কারিগরের মত সেই কাজে সফল। আপনাকে আমার হৃদয়ের উষ্ণ অভিনন্দন জানাই। অনিল বিশাসের আপনার page like করার অনুরোধে লেখাটা পড়ার সুযোগ হ'ল। লেখাটা পড়তে পারার জন্য তাঁকেও জানাই আমার অভিনন্দন।,0,celebrity
" আমার মনে হয় আমাদের বাংলাদেশ যে পৃথিবীর অন্য দশটা দেশ থেকে ভিন্ন তার একটা বড় কারণ, মুক্তিযুদ্ধের পর এই দেশে অনেক মা ঘর থেকে বের হয়ে সংগ্রাম শুরু করেছেন। বেঁচে থাকার জন্যে সেই সংগ্রামের কথা কতোজন জানে? মুক্তিযোদ্ধারা যুদ্ধক্ষেত্রে যে যুদ্ধ করেছে মুক্তিযুদ্ধের পর আমাদের দেশের সেই মায়েদের যুদ্ধ তাঁদের থেকে কোনো অংশে কম নয়। আমরা কী সেটা মনে রাখি?'' (y) (y) (y)",0,celebrity
"আপনার জানার কোন আগ্রহ আছে বলে তো আমাদের মনে হয় না,বিকজ আপনি তো সব সময়ই বলেন-আপনি নাকি পত্রিকা পড়া ছাড়া আর কিছুই বুঝেন না...আগ্রহ ও পাননা.... তাহলে আপনাকে জানিয়ে লাভ কি বলতে পারেন? পরে তো বলবেন এসব আমি বিশ্বাস করতে পারছি না,নিশ্চই এগুলো গুজব... শেখ হাসিনার সরকারের পক্ষে এসব করা কখনই সম্ভব না।",0,celebrity
মৃত মানুষ জেগে উঠল কেমনে???,0,celebrity
ফেইসবুক কি আমি জানি না স্টাটাস কি আমি জানি না লাইভ কি আমি জানি না  খালি জানি কেমনে চাটতে হয় সকালে চাটতে হয়  বিকালে চাটতে হয় রাইতে চাটতে হয়  জয় বানলা,0,celebrity
"আমাদের ভাইস চ্যান্সেলররা বিশ্ববিদ্যালয় মঞ্জুরী কমিশনকে মানেন না, শিক্ষামন্ত্রীর কথা শুনতে রাজি নন, কিন্তু মাননীয় প্রধানমন্ত্রীর অবাধ্য হওয়ার সাহস মনে হয় তাদের কারোরই হবে না।",0,celebrity
কারো কাছে মতিয়া আপার গালি দেয়ার ভিডিও থাকলে স্যারকে দেখান।,0,celebrity
আবার মদ খাবো আর কমেন্ট পড়বো 😂 হাসতে হাসতে ক্রশ করে পড়ে যাবো,0,celebrity
"পোস্টমর্টেম....  প্রথম কথা হল আপনি সব কিছু মুক্তিযুদ্ধের ফিল্টার দিয়ে দেখেন। কারন ওটাই আপনার কাছে সব কিছু। আপনি মুক্তিযুদ্ধ দেখেছেন ৭১ সালে তাই....  ডিয়ার স্যার! আমরা এখন আছি ১৮ সালে।  ৭১ আমরা দেখিনি। যা দেখছি চারপাশে তাই আমাদের সম্বল হওয়ার কথা,  গর্ব করার কথা। তো বলেন তো কি দেখছি আমরা?  আমরা দু'চোখে দেখছি এদেশটাই এখন দু'ভাগ হয়ে গেসে।  একদল জুলুম করেই যাচ্ছে আরেক দল শুধু খেয়েই যাচ্ছে৷ স্বাধীনতা? সেতো এখন যাদুঘরে থাকে।  মায়ানমারের মত পিচকি রাষ্ট্রের হেলিকপ্টার ঠেলে এদেশের সীমান্তে এসে ঘুরে যায় হরহামেশায়৷ ভারতের সরকার দলীয় নেতারা  এদেশ টা দখল করার হুমকি দেয়।  তখন কোন চেতনাবাজের ফিল্টারে সেসকল হুমকি ধরা পড়েনা। পড়বেই বা কিভাবে!  দেশ টা ভরে গেছে রিয়েল রাজাকারে। সব ভারতীয় রাজাকার৷ এরা ভারতের পা চাঁটতে পারলেই খুশি। এদের কে চিনেন স্যার?  ২য় কথায় আপনি বললেন।  কোটা আন্দোলনের একটা ছেলে বুকে রাজাকার লিখল বিধায় আপনি ওদের কে সমর্থন দেয়া বাদ দিয়ে গভীর ভাবে চিন্তা করলেন' কোথাও কোন ভুল হচ্ছে'  আসলেই স্যার৷ অবশ্যই ভুল হয়েছে৷ ছেলে টা তার বুকে আপনাদের উপাধি লিখে দাঁড়িয়েছিল৷ এটা ভুল ছিল। তার লেখার দরকার ছিল 'স্যার! তুই রাজাকার'  যে কিনা সামান্য সার্কাজম বিদ্রুপে প্রতিবাদ বুঝেনা সে কিভাবে ড্রোন বানায়? ভাল কাজ যারা করে তাদের কে যখন সরকারী লোকেরা রাজাকার আখ্যা দেয় তখন আর আপনার রাজাকার নিয়ে বই লিখতে ইচ্ছে করেনা? লিখেন বই লিখেন। বইয়ের নিচে কমেন্ট করার সুযোগ রাইখেন 😂  সবগুলি অহেতুক কথার যুক্তি খন্ডাতে পারতাম বাট এতবড় কমেন্ট এলাউড হবেনা। তাই শেষকথা বলি। আপনাকে এ জাতি অনেক আগেই চিনে ফেলেছে৷ সো প্রাপ্ত বয়স্ক দের কাছে বুদ্ধিজীবি সাইজা বুদ্ধি কপচানো ব্যাবসা অফ করেন।  বাচ্চাদের জন্য ভুতের বই লেইখা পেট চালান সেটাই উত্তম।  আমি হুমায়ুন আহমেদ স্যারের প্রায় ২০০ টা বই পড়েছি৷ মৃত্যুকালে হুড়মুড় করে কেঁদেছি। আমি মুক্তযুদ্ধ নিয়েও তার ভাবনা দেখেছি। অসাধারন!  মজার কথা হলো। আমি  আপনার মাত্র একটা বই পড়েছি। তখনই লেখায় কেমন 'চোর' চোর ভাব পেয়েছি। আর রুচি হয়নি।  আশা করি বুঝতে পেরেছেন।",0,celebrity
সুষ্ঠু নিয়মে সমন্বিত ভর্তি পরীক্ষার অবশ্যই দরকার আছে। আমরা মেয়েরা দূরের ভার্সিটিতে পরীক্ষা দিতে পারি না। হাতে গোনা কয়েকটি পরীক্ষা দিয়ে ভাগ্যের ওপর নির্ভর করতে হয়  যথেষ্ট হাস্যকর।,0,celebrity
কেউ (!!?) জীবনের মায়ায় গর্তে লোকায়!! আর কেউ জীবনের মায়া ত্যাগ করে মাতৃভূমি রক্ষায় যুদ্ধের দামামা বাজায়।,0,celebrity
নিশ্চই এবোভিন ট্যাবলেট খাচ্ছেন নিয়মিত।  তা না হলে হড় হড় করে বমি করে দেয়ার কথা।  নাহ ট্যাবলেটটা আসলেই ভালো,0,celebrity
আইছি কমেন্ট পড়বার 😃 বশির আহমেদ,0,celebrity
এত দিন পরে আপনার লেখা দেখে বমি পাচ্ছে । ওয়াক থু ।,0,celebrity
অনেক ধন্যবাদ সার অতি সুন্দর একটা লেখার জন্য। সারা দেশের মানুষের মনের কথা লিখেছেন। খালেদা সব দিক থেকে শেখ হাছিনার কাছে পরাজিত হয়ে এখন আমাদের ভবিষ্যত প্রজন্ম এসেসসি পরীক্ষার্থীদেরকে জিম্মী করেছে। এতেও কোন লাভ হবে না ইনশাল্লাহ।,0,celebrity
"""জাফর  ইকবাল  তো এটা  লুচ্চা!"" You should be ashamed of your comment! Are you out of your mind and do u have any idea the honorable man you are speaking about. Are you a son of any war criminal Mahadi Hasan",0,celebrity
"যেসব কুলাঙ্গার ভেবেছে স্যার ফিরে আসবেন না, তারা জানুক.. আমাদের একজন স্বপ্ন দেখানো শিক্ষক আছেন.. সুস্থ ভাবে ফিরে আসুন স্যার, আপনার অপেক্ষায় আছি আমরা!.. <3 <3",0,celebrity
"স্যার, আপনার ফ্যানরা আপনাকে মহান হিসাবে বিশ্বাস করে। আমিও করতাম এক সময়। কিন্তু মহান হিসাবে নয়, একজন মানুষ কীভাবে এই নির্লজ্জ ভোট ডাকাতিকে ইনিয়ে বিনিয়ে জায়েজ করতে ডাকাত সর্দারকে অভিনন্দন জানাতে পারে !  কীভাবে পারে জাতির ত্রাণকর্তা সেজে, জাতিকে ভবিষ্যৎ দেখানোর নাম করে এক অন্ধকার স্বৈরতন্ত্রের দিকে ধাবিত করতে ! আমার লজ্জা হয়, আপনাকে চিনতে আমার এত দেরী হয়েছিল। আপনার প্রতি রইল আমার সহস্র অভিশাপ। আমার বাকস্বাধীনতা হরণে আপনি নির্মম, নির্লজ্জ সহায়তাকারী। আমার বাকস্বাধীনতাকে আপনি এমন পর্যায়ে এনেছেন, আমার অভিশাপ দেয়া ছাড়া আর কোনো প্রতিবাদ করার ক্ষমতা নাই।",0,celebrity
আমরা যে কতটা অধঃপতিত জাতি তা কমেন্ট বক্সই বলে দেয়।,0,celebrity
"আপনি কি কবর থেকে উঠে আসলেন নাকি!!আপনার নাম শুনলে বমি আসে আগে ভালবাসতাম আর এখন করি ঘৃণা,জানাই ধিক্কার।লজ্জা কই গেছে??মুখ উঠাই কথা বলতে আসছেন।",0,celebrity
"স্যার', স্যার বলব কিনা জানি না। যাহোক আপনাকেই বলছি। 'রাজাকার' উপাধিটা ছাত্ররা গ্রহণ করার কারণটা কি আপনি আপনার 'ইন্টারনেট ঘেঁটে' বার করতে পারেন নাই? এই উপাধিটার সোর্স কে বা কারা সেটাও কি আপনি জানতে পারেন নাই? :) হাস্যকর। উনার নাম নিলে আপনার তো আবার চাকরি থাকবে না। আমি মতিয়া চৌধুরীর ব্যাপারে বলছি না কিন্তু। :)   হ্যাপি দালালি। (y)  এই ফিল্ডে আপনার সাকসেস কামনা করি। ভাল করছেন।",0,celebrity
স্যার আমি আপনাকে অনেক পছন্দ করি & ভালোবাসি ।দোয়া করি সুস্থ হয়ে উঠুন ।,0,celebrity
"৭ নাম্বার অপশনটা ভালো লাগছে,এইটা অবশ্যই প্রত্যেক রাজনৈতিক দলের ইশতিহারে থাকা দরকার এবং ছাত্রছাত্রীদের এই অভিশাপ থেকে রক্ষা করা উচিত",0,celebrity
"মি: জাফর, আপনি চোখে কালো চশমা পরে আছেন, আমি বিশ্বাস করি না। আপনি দালালি করছেন। এটাই স্বাভাবিক...  You should resign from all type of social activity. Nothing is left to learn from u.",0,celebrity
আহা!কি পাগল দেখলাম রে ভাই।,0,celebrity
"চামচার বাচ্চা,চামচিকা,",0,celebrity
"আবার প্রশ্ন ফাঁস হল,এবার শিক্ষক নিবনধন পরীক্ষার। ১০০ তে ১০০।জানি না এখান থেকে যে শিক্ষক নিয়োগ পাবে তারা ছাত্রছাত্রীদের কি শিক্ষা দিবে এবং এই সরকার আমাদের কি উপহার দিতে চলেছে.........।",0,celebrity
আপনি কিভাবে এই চামরাহীনমুখ দিয়ে মিথ্যা বলেন অলটাইন?,0,celebrity
সময়োপযোগী লেখক,0,celebrity
"আমার এক ছাত্র টেস্ট পরিক্ষায় ৬ বিশয়ে ফেল,, ফাইনালে গল্ডেন আ+,,,,,আমার অনেক লজ্জা লেগেছিল,,,, আপ্নাদের সাথে শেয়ার করলাম।।।। ",0,celebrity
"স্যার আপনার মাথা কি ঠিক আছে?দুর্নীতি করে যে সরকার আসছে সে করবে দুর্নীতি প্রতিরোধ 😂 আর আপনার চেতনার ল্যাউড়া এত উত্তেজিত থাকে কেন সবসময়, যে অন্যায়কেও সমর্থন দেন অবলীলায়। আপনাদের অবচেতন মন হলো ক্রমিনাল মাইন্ড,জাস্ট একটা মুখোশ পরে আছেন।আপনার পক্ষে গেলে সব অন্যায় ন্যায় আর পছন্দ না হলে ন্যায়ের দোকান খুলে বসেন।",0,celebrity
এরে তোরা কেউ আমার লুঙ্গির গিট্টু টা লাগাই দে.. ইস ঠা ঠাশ পড়তে পড়তে গিট্টু খুলে গেল...,0,celebrity
না পারেননা গর্তজীবি লেখক,0,celebrity
"সার শুধু কিতা ভাষার মাস নাকি, বাসায় নিয়ে খেলার মাসও😂",0,celebrity
সহমত ভাই,0,celebrity
হর হর করে  বমি আসি গেলো 😅 স্যার,0,celebrity
"সুখ পাখিরে আয় ফিরে আয়  আয় ফিরে আয়, আয় ফিরে আয়",0,celebrity
অনেক বড় ভীর গর্তে লুকিয়ে ছিলেন,0,celebrity
মুক্তিযুদ্ধ কি ভোট কেন্দ্র দখলের জন্য বা বিনাভোটে নির্বাচিত হওয়ার জন্য?,0,celebrity
লজ্জা শরমও নাই!   ঘুমের ট্যাবলেট মেবি বড় সাইজের ছিল।,0,celebrity
"স্যার,নির্বাচনে দাড়াইলেন না কেন? যা করেছেন এই ক-বছর, নিশ্চিত নমিনেশন পেয়ে যেতেন। আপনি তো আবার পরীক্ষিত........... স্যার মুক্তিযুদ্ধ নিয়ে যে ভাবে কথা বলেন তাতে তো মনে হয় আপনি বোধহয় মিত্রবাহিনীর প্রধান ছিলেন!! সবার জন্য মুক্তিযুদ্ধ বিষয়ক সাধারন জ্ঞানের প্রশ্ন,  জাফর স্যার কত স্টারের জেনারেল ছিলেন?",0,celebrity
"পাকিস্তান আমলে পূর্ব পাকিস্তানের ( বর্তমান বাংলাদেশের ) জন্য সরকারি চাকরির ক্ষেত্রে কত শতাংশ কোটা বরাদ্দ ছিল ????  যাদের রক্ত , আব্রু , পঙ্গুত্ব আর সাহসিকতার উপর ভর করে আজকে মেধা কোটা ভোগ করছেন , তাঁদের সম্মানের পরিধি কমিয়ে “আপনি মেধাবী” চাকরি হয়তো পাবেন  সাথে “ তুই রাজাকার উপাধি “....",0,celebrity
"অসাধারণ লেখনী আপনার,দয়ে করে নিজেকে অসুস্থ রাজনীতির সাথে না জড়িয়ে আপনার নীতিতে চললেই হলো।আমার একবারের জন্যেও মনে হয়না রাজনীতির লেজুড়বৃত্তি ছাড়া আপনি চলতে পারবেননা।",0,celebrity
একজন স্বনামধন্য অধ্যাপককে এভাবে অপমান করা উচিত না,0,celebrity
"শেখ মুজিবুর রহমান রাজনীতি ছাড়া আর কোন পেশায় জড়িত ছিলেন কি? না থাকলে ধানমন্ডির মতো অভিজাত এলাকায় ৩২ নম্বরের বাড়িটি কীভাবে করেছিলেন? তাঁর আয়ের উৎস কী ছিল কেউ জানাবেন কি? শেখ মুজিব নিহত হওয়ার পর তাঁর ব্যক্তিগত বাসভবনে পাওয়া গিয়েছিলঃ * হীরা, মুক্তা, প্লাটিনাম ও স্বর্ণালঙ্কার ৭ লাখ ৮০ হাজার টাকার * বাংলাদেশী মুদ্রা নগদ ৯৪ হাজার ৪৬১ টাকা * ৩টি ব্যক্তিগত মোটর গাড়ি * বৈদেশিক মুদ্রা ১৭ হাজার ৫শ’ টাকার * বিদেশি রাষ্ট্র প্রদত্ত প্রায় ১ লাখ টাকার উপহার সামগ্রী * বাতিলকৃত একশ’ টাকার নোট ৬২১টি * ১টি ভারি মেশিনগান, ২টি হাল্কা মেশিনগান, ৩টি এসএমজি, ৮টি স্টেনগান, ১০টি আধা স্বয়ংক্রিয় রাইফেল, ৬০টি গ্রেনেডসহ গোলাবারুদ, ইত্যাদি। [সূত্রঃ দৈনিক বাংলা : ১৪ সেপ্টেম্বর, ১৯৭৫]",0,celebrity
ফেসবুক কেন একটা মাদারচুদ রিয়েক্ট দেয় না ।আপনার লেখালেখি দেখলে মাদারচুদ রিয়েক্ট টা দিতে বড্ড ইচ্ছা হয়।,0,celebrity
দেখা যাক কি হয়। এই বিষয়ে আপনি অনেক লেখালেখি করেছেন। যদি সত্যি সত্যি এরকমটা হয় তাহলে আপনার কষ্ট সার্থক হবে। আর একটা কথা বিশ্ববিদ্যালয়ে বেশি ভাগ মেয়েরা ছেলেদের তুলনায় কম ভর্তি পরিক্ষা দিয়েছে কেন জানেন?   কারণ তাদের মা বাবা বোঝতে পারছেন মেয়েদে বুদ্ধি হাটুর নিচে। তাই মেয়েদের তুলনায় ছলেরা ভর্তি পরিক্ষা বেশি দেয়।      বোঝলেন স্যার......,0,celebrity
আপনাদের মত কিছু শিক্ষিত দালাল আছে যারা শুধুমাত্র নিজেদের স্বার্থে দেশও জাতির সাথে তামাশা কর যাচ্ছে প্রতিনিহত। এখন আর দালালী করে লাভ নাই পাবলিক এখন আপনাদের মতলব বুঝে!,0,celebrity
"আপনাকে নিয়ে সবাই আড়ালে হাসাহাসি করে,ভাল্লাগছে অনুধাবন করতে পারছেন৷",0,celebrity
"আশার গুরে বালি না পড়ে কেননা আমাদের দেশে কোন ভাল উদ্যোগই আর ভাল থাকে না,তখন মনে হয়, ছাইরা দে মা কাইন্দা বাঁচি...।",0,celebrity
কি ব্যপার শীতে সবাই জমে গেল নাকি? মজার মজার কমেন্ট পড়বো বলে ঘাপটি মেরে বসে আছি কিন্তু তেমন মজার কোন কমেন্ট পাচ্ছিনা।,0,celebrity
স্যার আমার উত্তর আসে (x = 5+10i & y = 5-10i) অথবা (x = 5-10i & y = 5 + 10i)। উত্তর  কি ঠিক স্যার?,0,celebrity
"স্যার আপনি যে এতো ভীতু আগে জানতাম না। সত্য কথা বলার সাহস টুকু আজ আপনার নেই৷ একাত্তরে আমাদের বুদ্ধিজীবীরা পাক হানাদের বিরুদ্ধে দাড়িয়ে  প্রাণ দিয়েছিলেন।  আপনাকে অন্তত দাড়াতে হতোনা ।  শুধু ছাত্র সমাজ চেয়েছিল আপনি ন্যায়ের পথে কথা বলুন। তাদের পক্ষে কথা বলুন।  তাদের ভুল গুলি সুন্দর ভাবে তুলে ধরুন ।  এটাও আপনি পারেননি। এর থেকেই বুঝা যায় আপনি কত  ভীতু। শিবির করে আমার এরকম এক বন্ধুকে আপনার বই পড়িয়ে আপনার  ফ্যান বানিয়েছিলাম। কিন্তু এখন বুঝেছি আমার আসলেই তা উচিৎ হয়নি।    আস্তিক নাস্তিক যে যাই  বলুক আপনাকে,  আমি আপনাকে অনেক সম্মান করতাম৷ কিন্তু তা এখন  অতীত। শুধু আমি না অনেকেই আপনাকে সম্মান করতো । কিন্তু প্রত্যেকের কাছেই তা  অতীত৷ ভাল থাকবেন স্যার৷",0,celebrity
অ্যাগো কত তামাসা দেখমু😁😁,0,celebrity
ওমা? সার দেহি বাঁইচ্চা আছেন....!,0,celebrity
",,",0,celebrity
এই যুদ্ধকালীন সময়ে বই মেলায় গেলে বেঁচে ফিরব ত!!!যে যাই বলুক না কেন জীবনের চেয়ে মূল্যবান কিছু হতে পারে না*,0,celebrity
"উনি না বমি করতে করতে মারা গেছেন, জানাযাও তো দিলাম... ফেসবুকে আসলেন কিভাবে...  নিশ্চয় বিএনপি-জামায়াতের চক্রান্ত..",0,celebrity
স্যার হড় হড় বমি জনিত কারনে পোস্ট লেখার সময় পাননি।আপনারা ভুল বুঝবেননা।,0,celebrity
"Well Approach Sir. আশা করি ইঞ্জিনিয়ারিং ইউনিভার্সিটি, মেডিকেল কলেজ, পাবলিক ইউনিভার্সিটি কমটির সদস্যরা ২০১৪ সালের বিপর্যয় এর কথা চিন্তা করে এক্সাম নিবেন। H.Sc পরীক্ষার রেসাল্ট নুন্যতম পর্যায়ে রেখে, রিজিওন ভিত্তিক (ঢাকা, রাজশাহি,খুলনা......) এক্সাম ভেনু পরিসর বাড়িয়ে সিলেকশন হলে সকল আসল মেধাবীরাই আসবে। দেশের সরকার, শিক্ষামন্ত্রি এ সকল ব্যাপারে চেতনাসিন থাকতে হবে। আগামী প্রজন্ম যাতে ধ্বংসের পথে না যায় সেদিকে সরকারের চোখ রাখার জন্য অনুরোধ জানাচ্ছি। দেশের আগামী ভাবমূর্তি উজ্জ্বল করার জন্য তারাই সম্বল যারা সত্য ও ন্যায়ের পথে থেকে বড় হবার স্বপ্ন দেখে।",0,celebrity
"স্যার আমি আপনার অনেক বড় একজন ভক্ত ছিলাম কিন্তু যেদিন আপনি বললেন আমাদের সফটওয়্যার  ইঞ্জিনিয়াদের জন্য আপনি আরো কিছু অপ্রয়জনীয় সাবজেক্ট সাপোর্ট করে বিশ্ববিদ্যালয় বোর্ডে চিঠি দিয়েছেন সেদিন আমি আপনাকে সফটওয়্যার  ইঞ্জিনিয়াদের রাজাকার বলে জানি 😁 ,কিন্তু আজ জানতে পারলাম যে আপনি ৭১ এর সময় রাজাকারের মতো ছিলেন। স্যার ৭১ এ ইঁদুরের গর্তে ছিলেন 🤣এখন তো আর সেই সময় নেই তাই যে যা বলুক আপনি ৫২ তে ফিরে যান😩 , এই বয়েসে কিছু হয়ে যেতে পারে দেশের মানুষ খেপালে ,আর আমার নানী (প্রধান মন্ত্রী ) আপনাকে কিন্তু শুধু এয়ার আম্বুলেন্সে করে ঢাকা এনেছে পাগলামি দেখার জন্য। সরি স্যার ভেটকানি মার্ক কমেন্টের জন্য 🙈",0,celebrity
ওনি খুব শিক্ষিত মানুষ তো। তাই safety first কথাটা ভালো করে বুঝেন।একবার কুপ খাইয়া শিক্ষা হইয়া গেছে।তাই এখন নিরাপদে থাকতে পছন্দ করেন।,0,celebrity
"একপক্ষ নিয়ে কথা বলা ছাড়ুন।আপনাদের মত বিবেকবান লোকেরা যদি মনে করেন নির্বাচন সুষ্ঠ হয়েছে, দেশের মানুষ আয়মালীগকে বিজয়ী করেছেন। তাহলে তো দেশের মানুষ পুরিষে ডুব দিয়ে আত্নহতা করা উচিত। ক্ষমতাসীনরা ভোট চুরি করে নিজেদের বিজয় দাবি করছে।",0,celebrity
"এজন্যই স্যার কে ভাল্লাগে, কারণ তিনি অ্যামেরিকাতে যান নি।একজন মন্ত্রী অ এমন চান্স  পেলে বাংলাদেশে থাকত না। আপনার মত ভালো মানুষ ইউরোপ,অযামেরিকাতে থাকে।আপনার উচিৎ ছিল এই অসভ্যদের দেশে না আসা,অ্যামেরিকাতে থেকে যাওয়া।",0,celebrity
দিন দিন হাসির পাত্র হয়ে যাচ্ছেন  :-),0,celebrity
যুদ্ধং শেষ হওয়ার পর যেমন গর্ত থেকে বের হয়েছিল।।। এখন আবার আন্দোলন এর শেষ পর্যায়ে এসে গর্ত থেকে বের হয়ে এক ইতিহাস লিখলেন।।।এই বালসাল পড়ার টাইম নাই।।আপনি ঘুমান।।।রাত বাড়ছে হাজার বছরের সেই পুরনো রাত।।।।,0,celebrity
হেয় কি কমেন্ট দেখে না?,0,celebrity
ইতিহাস গড়ার পথে।জয় বাংলা,0,celebrity
এ দেশে আর মনে হয় এটা বন্ধ করা সম্ভব হবে না!,0,celebrity
নাইষ লিখছেন!! বাট বমি করলেন না তো?? এখানেও তো ছেলে মেয়েরা খারাপ ভাষা লিখছে সেটা বললেন না তো??চাকরী যাবে??,0,celebrity
এ দেশে কোদাল ব্যাবসা নিয়ে লিখলে আর জনপ্রিয়তা পেতেন,0,celebrity
কমেন্ট পড়তে আসছি,0,celebrity
চেতনা ব্যাবসায়ীর ঘুম ভাংছে তাহলে।,0,celebrity
দয়া করে সবাই সিরিয়াল ধরুন :),0,celebrity
ইন্না-লিল্লাহি.......😹 আমার পশম ভরা বুকে অনেক কষ্ট লুকিয়ে আছে স্যার এর জন্য। কেউ জাফ্রাকবাল স্যার কে গালি দিবেন না বুজলেন।😭😭😭😭,0,celebrity
দেশে যদি চাটুকারদের দয়া না করতো তবে তোমার মত চাটুকার ভাত খাইতে ভাত পাইতা না,0,celebrity
সত্যিই আমি বিস্মিত স্যার!  আপনি তাহলে এই ধর্ষণের খবর পড়েছেন!  আপনার শুভবুদ্ধির উদয় হোক। অনেক ভালবাসা আপনার জন্য স্যার।  কারণ ভালবাসায় নাকি পাথরেও ফুল ফোটে। আমাদের ভালবাসায় আপনি মানুষের মতো মানুষ হবেন এই আশা করতেই পারি।  নিরাশ কইরেন না স্যার।,0,celebrity
আমরা লজ্জিত আপনার মত একজন গুরু পেয়ে,0,celebrity
"হেতের এত্তোবড় লেহা পড়ার টাইম নাই কিন্তু হেতের পোস্টে মজার মজার কমেন্ট হরে, হেগুলাইন আই মজা হরি পড়ি, আর ব্যাপক বিনোদইন লাগে ৷  হেতি আস্ত একটা হুদ্ধিজীবী হেইয়া আই বুজতাম পারি হেতের পোস্টে কমেন্ট চাই ৷ হেতি এউগ্গা সরকারি মাল ৷",0,celebrity
"এইসব ছাত্ররাই আন্দোলন করতে গিয়ে পুলিশের হাতে মার খাচ্ছে, স্কুল - কলেজ থেকে টিসি(TC) দিয়ে দেওয়ার হুমকি পাচ্ছে।  যখন সব উপেক্ষা করে মানবতার দায়ে আন্দোলনে নামছে, তখন শিক্ষকদের দ্বারা শারীরিকভাবে লান্ছিত হচ্ছে। প্রতিদিন রাস্তায়,  বাসে পরিবহন শ্রমিকদের মুখের অশ্লীল ভাষা শুনতে হয়, ইভটিজিং তো নিত্যদিনের ব্যাপার। বিচার হয়না, বিচার করে না। আমরা এই দেশকে কিভাবে ভালোবাসবো স্যার? আমরা এই দেশকে ভালোবাসতে চাই, স্বপ্ন নিয়ে বাচতে চাই। কিন্তু তা ভেঙে টুকরো টুকরো হয়ে গেছে। কোথায় যাবো স্যার? ঘৃণাগুলো এড়াতে চেয়েও এড়াতে পারি না। তাহলে এই ঘৃণাগুলো নিয়েই বেঁচে থাকবো স্যার? নিজের দেশকে ঘৃণা করে? কি নিয়ে স্বপ্ন দেখবো স্যার? অন্তত আপনার মতো মানুষদেরকেই আমরা ভালোবাসতে পারি, ভালোবাসি, আপনাদের থেকে অনুপ্রাণিত হই। আমাদেরকে কিছু বলুন স্যার...",0,celebrity
স্যার দেশে যে অবস্থা চলছে ১৯৭১ সালেও মানুষ এমন অশান্তিতে ছিলোনা...,0,celebrity
মাদ্রাসা!! মাদ্রাসা! !  মাদ্রাসা কি জংগি তৈরির কারখানা!!!!!,0,celebrity
স্যার গাঞ্জার দাম কি কমে গেছে???,0,celebrity
"ষাঁর তুই তোর আত্মীয়স্বজনদের এখনই বলে দে, তুই মরার পর যেন তোর জানাযার নামায না পড়ায়। নামাযে যখন তোর এতো চুলকানি, তাইলে তুই মরার পর তোর নামাযের জানাযা হোক এটা আমরা  চাই না।",0,celebrity
"বিশ্ববিদ্যালয়ের শিক্ষার্থীরা নিরাপদ সড়ক দাবি করে অন্যায়  করলেও স্যার আপনি খুব দয়ালু।  তাই ছাত্রলীগের কর্মকাণ্ডের সাথে এদের তুলনা করেন এবং নিরাপদ সড়ক দাবির জঘন্য অন্যায়ের ক্ষমা করা যেত বলে সরকারের বিরুদ্ধে খুবই হালকাভাবে সমালোচনা করলেন।  আপনি এটা বললেন যে, তা-ই বা কম কি  বাকি পয়েন্ট আর কিছু বললাম না :)",0,celebrity
"""কবর থেকে বলছি""",0,celebrity
আশ্চর্য !!  মৃত্যুর পড়েও উনি অনেক ভাল মন ভুলান লেখা উপহার দিতে পারে।   RIP : JAFAR IQBAL SIR.,0,celebrity
"“দেশের জন্যে যুদ্ধ করার সেই অবিশ্বাস্য গৌরব সবার জন্যে নয়, সৃষ্টিকর্তা অনেক যত্ন করে সৌভাগ্যবান কিছু মানুষকে তার জন্যে বেছে নিয়েছেন। বাংলাদেশে ভবিষ্যতে নিশ্চয়ই নোবেল বিজয়ী বিজ্ঞানী কিংবা সাহিত্যিক হবে, ফিল্ড মেডেল বিজয়ী গণিতবিদ হবে, অস্কার বিজয়ী চিত্র পরিচালক হবে, অলিম্পিকে স্বর্ণ বিজয়ী দৌড়বিদ হবে, ওয়ার্ল্ডকাপ বিজয়ী ক্রিকেট টিম হবে এমনকী মহাকাশ বিজয়ী মহাকাশচারী হবে কিন্তু আর কখনোই মুক্তিযোদ্ধা হবে না! এই সম্মানটুকু সৃষ্টিকর্তা যাদের জন্যে আলাদা করে রেখেছেন শুধু তারাই তার প্রাপ্য, অন্যেরা নয়।” -স্যার লেখাটার এ জায়গাটায় এসে আমি শিহরিত হয়েে উঠি, রোমাঞ্চিত হয়ে উঠি-গর্বে বুক ভরে যায়- আমার আর জীবনের কোনো চাওয়া-পাওয়া বা দুঃখ নাই- আর কি চাই জীবনে! মুক্তিযোদ্ধাদের সম্পর্কে এ ধরণের বক্তব্য আর কেউ দেয়নি। আমি যখন মুক্তিযুদ্ধের ট্রেনিং নিতে ভারতে যাই তখন আমার বয়স ছিল ১৫+ আমি সবচেয়ে অবাক হয়ে যাই আমাদের বাঞ্ছারামপুরে পাকিস্তান আর্মি মিত্র-মুক্তিবাহিনীর কাছে সারেন্ডার করেছিল ডিসেম্বরের ২২ তারিখ বিকালে- কিন্তু আপনার মুক্তিযুদ্ধের ইতিহাস বইয়ে এই ২২ তারিখ শেষ সারেন্ডারের কথাও উল্লেখ আছে- আপনি সেটা কীভাবে জানলেন! কারণ একাত্তরে বাঞ্ছারামপুর ছিল পৃথিবী থেকে বিছিন্ন একটি প্রত্যন্ত এলাকা। যাই হোক অনেক অনেক ধন্যবাদ মুক্তিযোদ্ধাদের সম্পর্কে এই প্রথম এধরণের মন্তব্য করার জন্য। -ফারুক ওয়াহিদ, ম্যানচেস্টার, ক্যানেটিকাট, যুক্তরাষ্ট্র। বি.দ্র. স্যার আমি আরেকদিন একাত্তরে আমার নিজের চোখে দেখা এবং আমার সামনেই ঘটনা- আগরতলার একটি শুধু একটি শিহরণমূলক উদাহরণ দিব- ঘটনাটি শুনলে আপনিও অবাক হয়ে যাবেন-  একাত্তরে আগরতলার জনগণের বা আগরতলার মায়েদের এই ঋণ আমরা কীভাবে শোধ করবো?  এবং আপনারও মন চাবে কৃতজ্ঞতাসরূপ একবার আগরতলা ঘুরে আসি!",0,celebrity
"এই সকল লোক যারা এমন একটি ব্লগ এর প্রচয়্দাতা হিসাবে কাজ করে  যেখানে কোনো একটি ধর্ম কে চরম ভাবে আঘাত করে লেখা লেখি হয় এবং আমি  মনে করি সেই সকল মানুষ সকল ধর্মের জন্যই শত্রু হিসাবে গণ্য হওয়া দরকার।  .কারণ এরা ধর্মে ধর্মে বিভেদ সৃষ্টি করার জন্য এনাফ। .আমরা  আরো জানি,  সবকিছু আল্লাহর দ্বারা নির্ধারিত হয়...এর মৃত্যু টা আল্লাহ এই ভাবেই  রেখেছেন। ...আশা করি সকলেই বুঝতে পেরেছেন",0,celebrity
"এইসব কোশ্চেন আউট করানোর পেছনে মুল কারণ সম্ভবত অভিভাবকরাই।তারা সন্তানের স্বার্থে যেন নয়, সন্তানের মঙ্গলের জন্য যেন নয় বরং সমাজে নিজ সন্মান বাড়াতে,প্রতিবেশীর কাছে গল্প করে শোনাবার উপকরণ হিসেবে সন্তানের ভালো রেজাল্ট চান।কারণ না হলে সমাজে তাদের মান ইজ্জৎ ধুলোই মিশে যাবে সম্ভবত। এই মান ইজ্জৎ বাঁচাতে, প্রয়োজনে চুরি বিদ্যা,প্রশ্ন ফাঁস ইত্যাদির সাহায্য নিতেও তারা পিছ পা হন না তাদের চাই একটাই জিনিস,ভালো রেজাল্ট।সন্তান কিছু পারুক বা না পারুক,শিখুক বা না শিখুক, একটা এ+ পেলেই হল তাদের। এ+ = সন্মান :-)",0,celebrity
"Zafar Iqbal is a Islam hater atheist,",0,celebrity
"""""আমি রাজাকার!!""????  যাহ,দুষ্টু! মশকারীও বুঝোনা,ব্যাঙ্গ ও বুঝোনা!  কী ছাইপাশ লেখক তুমি😛",0,celebrity
"অভিজিৎ রায় যে-ই হোক না কেন, উনি একজন বাঙালি - বাংলাদেশী। আর একজন বাঙালির মৃত্যু এই বাংলাদেশে এভাবে হবে? এটা সত্যিই হতাশা জনক এ জাতির জন্য। এমন নৃশংস হত্যাকাণ্ড বন্ধ না হলে স্বাধীন দেশের মাহত্ত্ব কোথায়? নিরাপত্তাহীন জীবন কি স্বাধীন দেশে মানায়? জাতি ধর্ম নির্বিশেষে দেশটা সকলের, আসুন দেশটাকে বাঁচাই সবই মিলে।",0,celebrity
এর চেহারা দেখতে চাই না!কোনো নাস্তিকের সমর্থন ছাত্রদের লাগবে না!,0,celebrity
"আমরা জাতী হিসাবে অনেক মেধাবি , কিছু খারাব মানুষের , কারণে আমরা আজ পথ হারা পথিক । বিশ্ব বিদ্যালয় কে তার নিয়মে চলতে দিতে হাবে। প্রতিটি  INSTITUTION কে তার নিয়ম অনুযায়ী চলতে পারলে দেশ তার গন্তব্য তে  যেতে পারবে ।",0,celebrity
গল্প পুরো পড়ে আমি আর নাই।শেষে এসে দেখি প্রথমে কি লিখছে ভুলে গেছি।লিখার বিষয়টুকু ও হারাই ফেলছি।বিদায় পিতিবী😰,0,celebrity
পাকি ছাগুগুলার একটু উন্নতি হইছে।হড়হড় করে বমি করা কমেন্ট কমছে কিন্তু ম্যা ম্যা করা ছাড়তে পারে নাই। এই ছাগুগুলার ধারনা স্যারের পোস্টে আইসা কমেন্ট করলেই পাকিস্তানের ভিসা পাবে। আফসুসসসস 😃😃,0,celebrity
উনি আবার মুরগি কবিরের জায়গা নিয়ে টানাটানি করতেছে নাকি,0,celebrity
কম বক্তৃতা দেবেন।লোক শুনবে।,0,celebrity
ষাড়ে নতুন বাণী প্রসব করেছে নাকি??,0,celebrity
কমেন্ট গুলা পড়তে আসলাম,0,celebrity
"এই শিক্ষা ব্যবস্থার কারনেই কিনা জানি না,আজকাল মা বাবাদের মধ্যে প্রতিযোগীতা চলছে খুব,শিশু নকল করুক আর যাই করুক,ফার্স্ট হতেই হবে,সবচেয়ে ভাল স্কুল এ পড়াতেই হবে(ডোনেশন দিয়ে হলেও),সমাজ কে দেখাতে হবে অনেক বড় স্ট্যাটাস তাদের। কিন্তু মাঝখান থেকে শিশুটি জীবন শুরু করে অন্যায় দিয়ে,আস্তে আস্তে এই অন্যায় কেই সে আপন করে নেয় তার পরবর্তী জীবনের জন্য।আজকালকার শিশুরা কিন্তু আর সেই ছোট্টটি নেই,ওদের জীবন আটকা পড়ে গেছে ডিজিটাল ওয়ার্ল্ড এর গ্যাজেটস এর মাঝে,যেখানে ইনোসেন্স নেই আছে শুধুই ম্যাচিউরিটি এবং ওভার কনফিডেন্স।",0,celebrity
এখনো লীগের দালালি ছাড়তে পারলেন না,0,celebrity
"আপনি নাকি অনেক বড় জ্ঞানী সাহিত্যিক? তবে ""আমি রাজাকার"" এর পেছনের সাহিত্যিক অর্থটা বুঝতে পারলেন না, এটা কিভাবে সম্ভব? এবং ছাত্ররা কোন প্রেক্ষিতে কথাটা বলেছিল সেটাও তো আপনি খুব ভালোভাবেই জানেন। তাহলে কাকে খুশি করতে এই নাটকটি লিখেছেন ছাত্রসমাজ জানতে চায়।",0,celebrity
"আপনার লেখা পড়ে বারবার প্রচণ্ড উৎসাহ পাই স্যার।নতুন উদ্যমে শুরু করি পথ চলা।এক আশ্চর্য রকমের শক্তি আছে আপনার লেখনীতে...আপনার দীর্ঘায়ু কামনা করি।এভাবেই আমাদের জন্যে, ভবিষ্যৎ বাংলাদেশের জন্যে আপনি সংগ্রাম চালিয়ে যান, সাদা-কালোতে..পরিবর্তনের আন্দোলনে...",0,celebrity
"(ঠিক কী কারণ জানা নেই, কোনো ভয়ংকর খবর পড়লে নিজের অজান্তেই আমি নিজেকে সে অবস্থানে কল্পনা করতে শুরু করি। পদ্মা নদীতে লঞ্চডুবির খবর পড়লে আমি কল্পনায় দেখতে পাই একটা লঞ্চ ডুবে যাচ্ছে, আমি তার ভেতরে আটকা পড়েছি, পানি ঢুকছে, মানুষ আতংকে চিৎকার করছে আর পানির নিচে নিঃশ্বাস নিতে না পেরে আমি ছটফট করছি। যখন একটা বাসে পেট্রোল বোমা দিয়ে আগুন ধরিয়ে দেওয়ার খবর পড়ি, তখন কল্পনায় দেখতে পাই আমি বাসের ভেতর আটকা পড়েছি, দাউ দাউ করে আগুন জ্বলছে আর আমি তার ভেতর দিয়ে ছুটে বের হওয়ার চেষ্টা করছি; আমার সারা শরীরে আগুন জ্বলছে।)  আপনার মত স্যার ঠিক আমার ও এরকম মনে হয়।",0,celebrity
"দাড়ি না রাখিয়া, রাখিয়াছেন মোছ এতদিনতো পাইলাম না আপনার কোন খোজ",0,celebrity
এক কালে আপনার বিশাল ফ্যান ছিলাম। এখন এটা ভাবলেই হাসি পায়। বত্ব এই স্ট্যাটাস কি থ্রিজি/ফোর জি ইন্টারনেট আসার পরে রচিত? UwU  হাহা দিয়ে পাশে আছি-,0,celebrity
বর্তমান শিক্ষা ব্যাবস্থা খুবই জঘন্ম,0,celebrity
কমেন্ট পড়তে আসলাম। (7)🤣,0,celebrity
স্যার তো কোদা‌লের ব্যাপা‌রে কিছু ব‌ল্লেন না!,0,celebrity
উনার প্রসব বেদনা উঠলে তিন দিন লাগে ডেলিভারি হইতে। 😂😂,0,celebrity
আমার রাতে ঘুম হয় না স্যার।আপনি কি খাইয়া এতো দিন ঘুমে ছিলেন জানলে উপকৃত হইতাম। 🙄🙄,0,celebrity
"ভিন্নমত থাকতেই পারে,,তাই বলে মেরে ফেলতে হবে।এটা কি ধরনের সভ্যতা। #মনটা সত্যিই ভেঙে গেছে। #জাফর ইকবাল স্যারের উপর হামলা। #কতটা নির্বোদ জাতির একটা অংশ। #একটা অংশের নির্বুদ্ধিতা,পুরো জাতির জন্য কলঙ্ক লেপন করছে। #স্যার দ্রুত সুস্থ্য হয়ে উঠুন। আমার ফ্রেন্ডলিস্টে কেউ যদি জাতির ঐ নির্বোদ অংশের প্রতি মৌনসমর্থন দিয়ে থাকেন।তাদের প্রতি বিনীতভাবে অনুরোধ করছি,আমাকে আনফ্রেন্ড করেন।পারত পক্ষ্যে ভিন্নমতের প্রতি শ্রদ্ধাশীল নন,এমন লোক থেকে দূরে থাকতে চাই। আল্লাহ্ আপনাদের শুভবুদ্ধি দিক,এটাই প্রার্থনা।",0,celebrity
অসাধারণ.........!!!!!,0,celebrity
এ দেশের  সবাধীনতার ইতিহাসকে বিকৃত করার  অধিকার দেশের মানুষ কাউকে দেয়নি,0,celebrity
"আপনাকে বর্ণনা করার জন্য যথেষ্ট একটা লাইন - ""খাওয়ার আগে ও মাইরের অনেক পরে"" । অনেকটা বাংলা সিনেমার পুলিশের মত । ""ঘটনা ঘটার পর এবং মুভী শেষ হওয়ার আগে "" ।",0,celebrity
সহজলভ্য তরকারি হল অালু। অার সেই অালুকেই অাপনি পটল বানিয়ে ছারলেন। সরি স্যার। অাপনার শুভবুদ্ধি ফিরে অাসুক।,0,celebrity
াাততকিতত্্ৃমমিকিমু কুম,0,celebrity
অসুস্থ জাতির কমেন্ট দেখলে থুথু আর আর কিছু আসে না,0,celebrity
দেশটাতো ধর্ষনের শিকার হয়েছে সেই কবে অাগে,0,celebrity
"স্যার, আপনি বেঁচে আছেন! আপনার এই ভূমিকা টা আমার কাছে সেই আমাদের চিরাচরিত বাংলা ছবির শেষ দৃশ্যে নায়ক-ভিলেনের মারামারির পর পুলিশ যেমন আসে ঠিক তেমনই মনে হচ্ছে!",0,celebrity
"গায়েবি জানাযাতে অংশগ্রহণের জন্য জেগে উঠছেন, স্যার? :D",0,celebrity
"আপনার রাজাকার নানাকে মুক্তিযোদ্ধারা খতম করেছে। অথচ ১৯বছরের তাগড়া যুবক হয়েও যাত্রাবাড়ীতে গর্তে লুকিয়ে ছিলেন। এখন মুক্ত বা স্বাধীন বাংলাদেশের আলো বাতাস গ্রহন করতে আপনার একটুও লজ্জা করে না ? পড়ালেখা করা লোক  এতো নির্লজ্জ কি করে হয় ?  আপনার কখনো যদি বিবেক জাগে। তবে বুঝবেন। আপনি রাজাকারের নাতি , রাজাকার হয়ে গর্তে ছিলেন। মুক্তিযোদ্ধাদের সাহায্যে বাহির হননি😡✊🏽",0,celebrity
কমেন্ট পড়তে আসছি😑,0,celebrity
কাপুরুষরা দেখতে ষাঁড় এর মত হয়!!,0,celebrity
গন্ডারের চামড়া,0,celebrity
ধুর কমেন্ট পড়তে আইসা আর পোস্ট পড়বার যাইতে পারতাছি না!!!  কৌতুহল জিনিসটাতো খুউউব খারাপ!!,0,celebrity
"এই বিকৃত মস্তিষ্ক এর চেয়ে ভালো কিছু প্রসব করতে পারবে না,এটা আগে থেকেই জানতাম। মাথায় আওয়ামী প্রেম গুদ্ গুদ করতেছে।",0,celebrity
"অভিজিৎকে হাসপাতালে নিয়েছে জেনে ""দোয়া"" করছিলাম যেন বেঁচে যায়, কিন্তু অভিজিৎ বাঁচল না।"" ---- আগ্রহী উৎসুক অন্তর অবহিত হতে চায়; দোয়া করেছিলেন কার কাছে ??? @ Muhammed Zafar Iqbal",0,celebrity
"মুক্তিযুদ্ধকে আর কত ধুবেন,আর তা দিয়ে আর কত পানি খাবেন? ঐ জিনিষরে বানাইছেন তিতা। যে ছাত্রলীগ বানাই রেখে যাচ্ছেন সামনে বিশ্ব বিদ্যালয় আর থাকে কি না দেখেন? আপনি একজন দালাল হিসেবে চির চিহ্নিত থকবেন।",0,celebrity
আল্লাহ তাআলা আপনাকে জান্নাত নসিব করুন। সবাইকে হেদায়েত দান করুন। দয়া করে আপনি আর কোনোদিন সাভার এ আসিয়েন না।  আর হ্যা কোনোদিন ভুলেও প্রতিক্রিয়া দেখিয়েন না রাতে ঘুমাতে পারবেন না।,0,celebrity
"খোলাচিঠি:প্রতিবাদ  শ্রদ্ধেয় জাফর ইকবাল স্যার, শুভেচ্ছা নিবেন।আশা করি আপনি এখন সম্পূর্ণ সুস্থ।আপনার উপর দিয়ে বয়ে যাওয়া ঝড় সামলিয়ে উঠেছেন ঠিকমত। স্যার,আজ আপনার লেখা : আমি রাজাকার, একটি আলোকচিত্র লেখাটি পড়লাম। স্যার,লেখাটি পড়ে যা অনুধাবন করলাম তা হল আপনকরল বার্তা পেয়েছেন অথবা ছাত্রদের দেয়া সঠিক বার্তাকে ভুলভাবে ব্যবহার করছেন!তাদেরকে আপনি ভুল ব্যাখ্যা দিয়ে ফাঁসানোর পায়তারা করছেন। স্যার,আপনার লেখাটা অনেক অস্পষ্ট বা অসম্পূর্ণ।   স্যার, এখানে একটা প্রশ্ন রাখি আপনার কাছে আপনি কি সাধারণ ছাত্রদের আন্দোলন করার সকল খবর ঠিকভাবে রেখেছেন অথবা জানতে চেয়েছেন কি কারও মাধ্যমে? স্যার,আপনি কি মতিয়া চৌধুরীর বক্তব্যের সম্পূর্ণ ভিডিওটা দেখেছেন কখনও?  আমি হলফ করে বলতে পারি আপনি তা করেন নি আর করার চেষ্টাও করেন নি!যদি ভিডিওটা দেখতেন তাহলে আসল ব্যাপারটা জানতে পারতেন, বুঝতে পারতেন। যদি আপনি আন্দোলনের সঠিক খবর রাখতেন তাহলে এমন বিভ্রান্তিকর লেখা প্রকাশ করতেন না।  স্যার,আন্দোলনকারীদের মূল স্লোগান ছিল """"চেয়েছিলাম অধিকার, হয়ে গেলাম রাজাকার।"""" অর্থাৎ অধিকার চাওয়ার কারণে আমাদের রাজাকারের বাচ্ছা রাজাকার বানিয়ে দেওয়া হয়েছিল। যা সুস্থ মস্তিষ্কের মুক্তিযুদ্ধের পক্ষের কোন ছাত্র বা মানুষ মেনে নিতে পারে না। আমরা, সাধারণ ছাত্রছাত্রীরা এই রাজাকার শব্দটিকে ঘৃণার চোখে দেখি আর আমরা এই আন্দোলনেও এটাকে একটা ঘৃণিত শব্দ হিসেবেই ব্যবহার করেছি।   রাজাকার যে শব্দটা বাংলাদেশে সর্বাধিক ঘৃণিত একটা শব্দ।সেই শব্দটার ক্ষেতাব দেশের আপামর ছাত্রদের উপর চাপিয়ে দেওয়া কোন সুস্থ মানুষের পক্ষে সম্ভব নয়। আর তাই সাধারণ শিক্ষার্থীরা এই রাজাকার বানিয়ে দেওয়ার প্রতিবাদ করেছিল এবং শব্দটিকে ঘৃণিত শব্দ হিসেবেই ব্যবহার করেছিল। স্যার,কিন্তু অত্যন্ত দুঃখের বিষয় আপনি সেটাকে ভুলভাবে ব্যাখ্যা করলেন।দাড়ি চিহ্ন আর আশ্চর্যবোধক  চিহ্নকে আপনি এক করে ফেলেছেন। স্যার,আপনি কি জানেন এই আন্দোলনে অনেক মুক্তিযোদ্ধার সন্তানাদি যুক্ত আছে? তারা কিভাবে মেনে  নিতে পারে যখন তাদেরকে রাজাকারের বাচ্চা বলে ক্ষেতাব দিয়ে দেন আপনারা।  স্যার,আমি আপনার এই ""আমি রাজাকার:একটি আলোকচিত্র ""লেখাটির প্রতিবাদ জানাচ্ছি এবং ঘৃণাসহকারে তা প্রত্যাক্ষাণ করছি।",0,celebrity
হ্যাশট্যাগ #Vote_For_Boat 🐸,0,celebrity
একদম মনের কথাগুলো লিখেছেন স্যার। আপনাকে অসংখ্য ধন্যবাদ।,0,celebrity
আজরাইল যখন নাকের ডগায় ঘুরে তখন খোদার কথা খুব মনে পড়ে😁😁,0,celebrity
অফ টপিক//  এই পেইজটার নাম দেখে মেজাজ বিগড়ে গেল। দেখেন তো কোন পদক্ষেপ নেয়া যায় কি না - https://www.facebook.com/Dr.Mohammad.Zafar.Iqubal,0,celebrity
কিছু মানুষ সারা জীবন আসুদা থেকেই যায় !!,0,celebrity
"""কোটা সংস্কার আন্দোলন"" কারীদের নিয়ে কোন লেখা আপনার জন্য মানায় না স্যার।আন্দোলনকারীরা কিছুটা হলেও আন্দোলন সফল করেছে।ওরা কতটা বুকচাপা কষ্টনিয়ে ""আমি রাজাকার"" কথাটা প্রকাশ করেছিল তা কি আপনি বুঝতে পারেন নি? আপনাদের মতো বুদ্ধিজীবীদের সমালোচনায় কত আন্দোলনকারীরা হামলার শিকার হলো।ইতিহাস বেঁচে থাকে সেটা ""৭১ বা ""১৮ হোক।",0,celebrity
",যারা আগে ছিল তেতুল হুজুর তারা এখন মিস্টি হুজুর,যারা এখন যুদ্ধাপরাধী,৯৬ সালে তারা ছিল সহযোদ্ধা।সত্যিই চুরি বিদ্যা মহাবিদ্যা,এতে ধরা পড়লেও অসুবিধা নেই",0,celebrity
"বেচারা জাফর ষাঁড়, জনগণ গায়েবানা জানাজা পড়ছে শুনে পোস্ট দিছে। 😱",0,celebrity
আসুন সবাই মিলে স্বাধীনতা বিরোধিদের বিরুদ্ধে যুদ্ধ ঘোষণা করি। ধর্ম ব্যবসায়ীদের রেহাই নাই।,0,celebrity
অচথা শিশুগুলোকে কষ্ট দেয়ার কি দরকার???   কেউ সাড়া বছরই প্রাইভেট পড়াচ্ছে। যাদের মাতাপিতা অসচ্ছল তারা পাড়ছে না। এতে হীনম্মন্যতায় ভোগছে এসব শিশু। বছর শেষে প্রশ্ন আউট। এতে এসব শিশুরা পরীক্ষা ও সরকারী নীতিমালা সম্পর্কে কি বেধ নিয়ে বেড়ে ওঠছে???,0,celebrity
মহান আল্লাহ পাকের নিকট সুস্থতা এবং দীর্ঘায়ু কামনা করছি।,0,celebrity
জাফর ইকবাল এর মোচের রহস্যা উৎঘাঠন করতে হবেই!  কি করলে এই কোদাল মোছ পাওয়া যাবে 😶,0,celebrity
লা হাওলা ওয়ালাকুয়াতা ইল্লা বিল্লাহ---বাণীতে আহসান হাবীব পেয়ারা।,0,celebrity
স্যার আমাদের দেশের মানুষ আপনার কদর বোঝে না | তাই আপনার উপর এমন নির্মম অত্যাচার করেছে পিশাচ এর দল | আপনি আমাদের জাতি হিসেবে ক্ষমা করবেন ‌| আমি মাননীয় প্রধানমন্ত্রীর কাছে বিনীত অনুরোধ করব যেন আপনার নিরাপত্তার জন্য এসএসএফ নিয়োগ দেন | আপনি আমাদের মাঝে অনেকদিন বেচে থাকুন এই দুআ করি |,0,celebrity
আমি ভেবেছিলাম ভোটের ফলাফল দেখে সবার মত আপনিও লজ্জিত হবেন। বুঝিনি BAL এর মত আপনারও লজ্জা নেই!,0,celebrity
"আপনার মত নির্লজ্জ, বেহায়া, বেশরম, বেয়াক্কেল, দালাল, চাটুকার এই বাংলার জমিনে কম আছে। ৭১এ মুক্তিযুদ্ধের সময় কাপুরুষের মত গর্তে ঢুকে ছিলেন সবাই জানে।  এখন আইছে আদর্শের ব্যবসা চুদাইতে।",0,celebrity
"কেউ নাড়া দিস না, কমেন্ট গুলো পড়তে দে।",0,celebrity
শীট!!!! ভুইলাই গেসিলাম এফবি তে বমি রিয়েক্ট নাই...:O মনে থাকলে এই পোষ্ট পরতাম না...:-/ এখন কি করি...;-),0,celebrity
খোদা আমাকে এই অবিশ্বাস্য সুন্দর পৃথিবীটিকে আরো কয়দিন দেখতে দেবে?,0,celebrity
ঘুম থেকে উঠে শুনলাম আপনি ফেসবুকে স্ট্যাটাস দিয়েছেন।তাই পড়তে,0,celebrity
আর কত দালালি করবেন? কেন তারা তাদের বুকে 'আমি রাজাকার' লিখল সেটা তো বললেন না একবারও???,0,celebrity
এখন দরকার ঘরে ফেরা৷ তারপর নিজেদের তৈরি করা। সেই জাইগায় নিজেদের নিয়ে জাওয়া যেখান থেকে নিজেই সংশোধন করতে পারবে সব আইন। নিজেই আইন প্রয়োগ করতে পারবে।,0,celebrity
"আপনি তো মরে গেছেন, কাল তো আপনার গায়েবী জানাজা, আপনি কি প্যারোলে জাহান্নাম থেকে মুক্তি পেয়েছেন নাকি?",0,celebrity
বমি বাবা,0,celebrity
আপনি বোধহয় এই দেশের লোকনা !,0,celebrity
এই কুত্তার  জন্মদিনে একটা কুত্তি উপহার দে,0,celebrity
"ওনার না গায়েবী জানাজা পড়ার কথা আমাদের কাল,মৃত ব্যাক্তি উদয় হল কোথথেকে 😲",0,celebrity
"""একটা সমস্যা না দেখার ভান করলেই কি সমস্যাটা মিটে যায়? সমস্যা মেটাতে চাইলে সেটাকে সবার আগে স্বীকার করতে হয়। দেশের সর্বোচ্চ মহল এই সমস্যাটা স্বীকার করতেই রাজি না। তাহলে সমস্যাটা সমাধান হবে কেমন করে?""",0,celebrity
পৃথিবীর সব দেশের বিমানবন্দরেও বাংলাদেশ থেকে বেছে বেছে মুক্তিযুদ্ধের স্বপক্ষের লোকদের সাপ্লাই দেওয়ার দাবি জানাচ্ছি। এর জন্য আলাদা একটা মুক্তিযোদ্ধা কোটা করা হোক।  ও একটা বিষয় মনে পড়ল। মুক্তিযুদ্ধের সময় আমেরিকা ছিল বাংলাদেশের বিপক্ষে। আপনি কোন জ্ঞানে এমন একটা মুক্তিযুদ্ধের বিপক্ষের দেশে ঘুরে বেড়াচ্ছেন? আপনার ঘুরে বেড়ানো উচিত জাপান ভারত এইসব দেশে। ছি মুক্তিযুদ্ধের চেতনা নিয়ে ছিনিমিনি খেললেন!!!,0,celebrity
স্যারের চিন্তাশক্তি ও স্মৃতিপট লোপ পেয়েছে।  স্যরকে কেউ পাবনার রাস্তাটা দেখাই দিয়েন।,0,celebrity
"আপনি কোন লেভেলের ছাগল? আমরা বুকের উপর ""আমি রাজাকার"" কথাটা কখনই ""রাজাকারদের"" সম্মান জানিয়ে লিখি নি। আমাদের ""রাজাকার"" উপাধি দিয়েছিল আপনাদেরই এক নেত্রী।তখন আপনি কোথায় ঘুমিয়ে ছিলেন? তখন গলার জোর কই ছিল? সেই কথাই কটাক্ষ করে আমরা নিজের বুকে কথাটা লিখেছিলাম।",0,celebrity
ভাল মানুষদের ভাল থাকা উচিৎ! এটুকু আশা করতেই পারি কিন্তু আপনিও নিরাশ করলেন। তবেই লেখক আপনি ভাল কিন্তু মানুষ..?,0,celebrity
"অভ্র ব্যবহার করুন , অত্যন্ত সহজ একটি লে-আউট",0,celebrity
কেউ ঠেলাঠেলি করবেন না।সাইডে ভাই সাইডে।সবাই সুযোগ পাবেন গালি দেয়ার।  লাইন ধরেনভাইয়েরা।,0,celebrity
"প্রিয় মীর জাফর স্যার, শাহবাগ মোড়ে আপনার গায়েবানা জানাজার আয়োজন করা হয়েছে। সবান্ধব যোগ দেয়ার আমন্ত্রণ রইলো।",0,celebrity
"Example 3.3: কেন ত্বরণ a = g ধরতে হলো, ব্যাখা করলে ভাল হত। বাকি সব কিছুর উপস্থাপন অসাধারণ",0,celebrity
আপনি যাবেন সেই সব আন্দোলনে যেই সব আন্দোলন দেশ ও জাতির জন্য ধ্বংস ডেকে আনবে।।। আপনি দেশ প্রেমিক নয়। দেশের প্রেত আত্বা,0,celebrity
"আমি যে ভাগ্যবান সেটা জানতে এখন আমার হাতের রেখা দেখার দরকার নাই। আমি ২০১৫ সালের এসএসসি পরীক্ষার্থী নই, এইটা জানাই যথেষ্ট!",0,celebrity
সুবিধাবাদী জ্ঞানীর চেয়ে অসুবিধাবাদী মূর্খ ও অনেক ভালো ৷ এতে দেশের উন্নতি না হতে পারে কিন্তুু ক্ষতি হওয়ার সম্ভাবনাতো কম ৷,0,celebrity
"একমত হতে পারলাম না, ""আমি রাজাকার"" মতিয়া ম্যম কে অপমান করা্র জন্য ব্যবহার করা হয়েছে। এই নরমাল বিষয় টি আপনার মত বুদ্ধিজীবী বুঝল না কেন তা আমি বুঝলাম না।",0,celebrity
"ছাত্রছাত্রী & লাখো জনতা যখন কোটা বিরোধী আন্দোলন করছিলো,তখন সাধারণ ছাত্রছাত্রী কে কৃষিমন্ত্রী বেগম মুতিয়া চৌধুরী রাজাকারের বাচ্চা বলে গালি দিয়েছিলো আপনি সেটা একেবারে জন্যও দেখেন নি জনাব???  তরুণ প্রজন্মকে সরকারি দল রাজাকার বলা মানে শাস্তিযোগ্য অপরাধ, তার পদত্যাগ করা উচিৎ। বাংলাদেশ এর প্রেক্ষাপটে প্রতিবন্ধী & উপজাতি কোটা ছাড়া কোন কোটা থাকা উচিৎ না। মুক্তিযোদ্ধারা মাসে মাসে ১০-১৫ হাজার টাকা,বিদ্যুৎ বিল ফ্রি, সৌর বিদ্যুত,চিকিৎসা আরও কত কি?? তার পরেও তাদের সরকারি চাকুরী তে ৩০% কোটা লাগে।সারাদেশ বাসী গাঙের জলে ভেসে এসেছে।দেশের লোজ কামলা খাটবে।চাকুরী করবে মুক্তিযোদ্ধার সন্তান রা।গাঁজাখোর এ দেশ ভরতি",0,celebrity
"সবচেয়ে অবাক আর খারাপ লাগে যখন আপনার প্রিয় মানুষগুলো আপনার বিরুদ্ধে কিংবা আপনার মতের বিরুদ্ধে কিছু বলে ফেলে। কলামটা পড়ার পর সবচেয়ে বেশি অবাক হয়েছি --- ১. 'আমি রাজাকারের বাচ্চা' কথাটা ছাত্রছাত্রী নাকি গর্ব করে বুকে টানিয়েছে,  স্যার মাননীয়া মন্ত্রী মতিয়া চৌধুরীর ভাষণের সময় মনে হয় আপনি অভারডোজ ঘুমের ওষুধ খেয়ে অবচেতন হয়ে গিয়েছিলেন এ জন্য আপনাকেকে আমমরা একটা সাজেশন দিবো আপনি ইউটিউব এর সার্চ অপশনে গিয়ে টাইপ করবেন 'রাজাকারের বাচ্চা বাই মতিয়া' উত্তর পেয়ে যাবেন।  ২.একাত্তর টিভির প্রচারণা দেখে, টকশোটা কোন চ্যানেলে দেখেছেন সেটা না বললেও হতো। ৩. আন্দোলন জমজমাট হয়েছে ঢাবি উপাচার্যের বাসভবন ভাংচুরে মাইরি স্যার আপনার এই কথা শুনে হাসি আটকাতে পারলাম না।  স্যার বিশ্ববিদ্যালয়ের শিক্ষার্থীরা রোদে-বৃষ্টিতে পুড়ে ভিজে কোন দলকে আপনার মতো হাইলাইট করে না।   যখন ১৬ বছরের শিক্ষাজীবন শেষ করে দুপুরের খাবার খাওয়ার পর রাতের খাবার যোগানোর পয়সা পকেটে থাকে না তখন আন্দোলন করে,  বুকের রক্ত ঝরায়, প্রাণ উৎসর্গ করে !",0,celebrity
জানতাম এই রকমই কিছু একটা হবে।,0,celebrity
জাফর ইকবাল বাগধারাটির অর্থ সময়ে সময়ে এত বদলায় কেন!!!,0,celebrity
কেউ ঠ্যালাঠ্যালি করবেন না....সুন্দর ভাবে লাইনে দাড়ান...সবাই বমি করার সুযোগ পাবেন....এটা সবার অধিকার..কেউ কারো অধিকার নিয়ে টানাহ্যাঁচড়া করবেন না.....😜,0,celebrity
আমার মতে পরীক্ষা বাতিল করাই শ্রেয়,0,celebrity
"আছালামুয়াইকুম স্যার ।  স্যার সমমানী লোকদের সমমান দেওয়া,  যাদের আর্দশে আমরা উজবীত হই,  আর তাদেরকে যদি হত্যা করা হয়।  তাহলে আমরা কার আর্দশে সামনের পথ ধরে  এগিয়ে যাব ....!..................",0,celebrity
আমি হড় হড়  করে বমি করে দিলাম কলাম দেখে আমার অপরাধ বলেন??,0,celebrity
"হবে, আপনাকে দিয়ে হবে। সবকিছু বিএনপি-জামাত টেনে আনার অপরিসীম ক্ষমতা আছে আপনার।",0,celebrity
"উনি নাকি এত বড় এত বড় রাইটার। মখা আলমগির এই হাগলডার চেয়ে অনেক ভালো ছিলো। ""রাজাকার "" ছাত্ররা কি সাধে লিখেছে...???? এই সামান্য জিনিস যার মাথায় আসেনা সে নাকি আবার একটা ভার্সিটির কি যেনো।।।। জানতে জানতে জানোয়ার হলে যে অবস্থা হয়।",0,celebrity
মদ খাবো আর কমেন্ট পড়বো 🍷,0,celebrity
সেই কোদাল খানা কই স্যার জাদু ঘরে উঠান আমার গফ দেখতে চায় :/,0,celebrity
প্রথমবার আপনার পোষ্ট পড়ে আর কমেন্ট পড়ে প্রচণ্ড হাসতে হাসতে চলে গিয়েছিলাম।অনেকক্ষনপর মনে পরলো আরে কোন রিয়েক্ট তো দেই নাই।সার্চ দিয়া আপনার আইডিতে ঢুকে হাহা রিয়েক্ট দিয়েই দিলাম।আপনি খুবই মজার মানুষ স্যার!সত্যিই খুব মজার মানুষ!!!  :v,0,celebrity
"স্যার আমি আপনার লেখা পড়ি না, কিন্তু কমেন্ট গুলো পড়ি.... মজা পাই।",0,celebrity
জাফর স্যারকে এমপি পদে দেখতে চাই😂😂,0,celebrity
গর্ত থেকে কবে বের হলেন স্যার?,0,celebrity
আপনি লাইভ বোঝেন না স্যার!!!! কেউ আমারে এক ফোটা বিষ দে,0,celebrity
"নিজের মাইয়ারে একটা বাঙ্গালী পোলার সাথে বিয়া দিতারেন নাই আবার আইছেন বাংলা ভাষার দায়িত্ব নিতে, আপনি এমুন পিছলা কেন স্যার?",0,celebrity
"স্যার আপনার জন্য অনেক অনেক শুভকামনা রইল,,,,,আপনি খুব দ্রুত আমাদের মাঝে ফিরে আসুন,,,,,",0,celebrity
ঢাকার ভিতর পাবলিক পরিবহনের একটারও চামড়া নাই কেন?  জাফর স্যার জবাব দ্যান?,0,celebrity
সিলেট শহরটা কবুতরের জন্য বিখ্যাত।  শাহজালাল মাজারে আছে কিছু জালালি কবুতর।  শাহজালাল বিশ্ববিদ্যালয়ে আছে একটা দালালি কবুতর।   -Arif Adnan bhai,0,celebrity
স্যার আপনাকে অনেক ভালবাসি :) আপনার মত সাদা মনের মানুষ হয়তো খুব কমই আছে :'(,0,celebrity
একটা মানুষ কয়বার মরে!!!,0,celebrity
"এসব নারীকে পুরুষের ভিড়ে ঠেলে দিয়ে তাদের সর্বস্ব লুট করার ফন্দি ছাড়া আর কিছইু না!  নারীদের প্রয়োজনে শিক্ষা-দিক্ষার দরকার হতে পারে।কিন্তু তার মানে এই না যে তাদের জন্য নিরাপদ পরিবেশ নিশ্চিত না করে হায়েনাদের পালের মধ্যে ছেড়ে দিতে হবে।মেয়েদের ইজ্জত-সম্ভ্রম,জীবন ঝুঁকির মধ্যে ফেলে তাদের শিক্ষাঙ্গনে,কর্মক্ষেত্রে পাঠাতেই হবে এমন কোন কথা আছে?তাদের সত্বীত্ত,তাদের জীবনের দাম কি এতই কম?যে বস্তুবাদী শিক্ষা আর কথিত উন্নয়নের নামে তা লুটপাট হতে হবে?যে পরিবেশে তা অনিরাপদ, সেখানো নিরাপদ পরিবেশ নিশ্চিত না করা পর্যন্ত পাঠাতে নিষেধ করা তো শতভাগ যুক্তিপূর্ণ।আল্লামা আহমাদ শফি সাহেবের কথা বাস্তবা এবং শরীয়তের দৃষ্টিকোন উভয় দিক থেকেই সঠিক।নারীদের সরলতার সুযোগ নিয়ে,উন্নয়নের ধোঁয়া তুলে তাদের বোকা বানিয়ে ঘর থেকে বের করে এনে ধর্ষণ করার মতলব যাদের তারাই কেবল হুজুরের কথার বিরোধীতা করতে পারে।",0,celebrity
আপনাকে কেন ?? ওরাতো পুলিশ !!! আপনার student .আপনাকে respect করেছে । যদি ওদের পিছনে লাগেন .....তাই আপনারে মাফ দিছে.......  .,0,celebrity
আসলেও তো। যতক্ষণ প্রতিটা মানুষ না ভাববে মারা গেছে ততক্ষন দেশ মরবে কেমন করে? দেশ তো আর কোন প্রাণী না যে কেউ এসে একটা গুলি করলেই খতম।,0,celebrity
"আমাদের শিক্ষা ব্যবস্থার এমন করুণ অবস্থার জন্য একমাত্র  দায়ী আপনি ৷ আপনি এক এক নতুন শিক্ষা পদ্ধতি চালু করে, আমাদের শিক্ষা ব্যবস্থার এমন হাল করেছেন ৷ কই আগে তো কখনো শোনা যায়নি, প্রশ্ন ফাঁসের কথা ৷ শুধু নকল টা ছিল ৷ আপনি হঠাৎ হঠাৎ করে নতুন শিক্ষা পদ্ধতির চালু করে, শিক্ষার্থীদের জীবনটা কে নষ্ট করে দিচ্ছেন ৷ বাইরে বিশ্বের সাথে চুক্তি করে ভিতরে ভিতরে আমাদের শিক্ষার পদ্ধতির মান টা ও নষ্ট করে দিতেছেন ৷ আর বাইরে সাধু সেজে আমাদের উপকার করার কথা বলছেন ৷ সব নষ্টের মূলে আপনার হাত ৷ দোহায় আপনাকে আমাদের ছেলে - মেয়েদের শিক্ষার জীবন নিয়ে খেলা করবেন না ৷",0,celebrity
উনি সুযোগলীগ করেন বোধহয়........,0,celebrity
"তরুণ সমাজের উপর আপনি হড় হড় করে যে বমি করছেন তা পরিষ্কারের যত চেষ্টা করেন ততই ব্যর্থ হবেন, কারন জাতি আপনার আসল রূপ দেখে ফেলেছে।   আপনি নিজেকে আইনিস্টাইন, সক্রেটিস ও এরিস্টটল এর মত জ্ঞাণী মনে করলেও  জাতি আপনাকে #বোধাই হিসাবেই মূল্যায়ন করবে।    আপনি তরুণ প্রজন্মের  মনের ভাষা ও যন্ত্রণা  বুঝতে দারুণভাবে ব্যর্থ হয়েছেন।  আপনাদের মত বুদ্ধিজীবীরা যেকোনো দেশের জন্য ভয়াবহ ক্ষতিকর।",0,celebrity
বাড়া,0,celebrity
মাঠে নামার প্রথম হুংকার টা তো জাফর ইকবাল স্যারই দিয়েছেন।   যদিও সেটা স্বপ্নে ছিল। 😷,0,celebrity
yes bangladesh beche ace tobe ghonotontoo nei sir,0,celebrity
সাপ্তাহিক ছুটির দিনে এই কমেন্টবক্সটা অসাধারণ একটা বিনোদনের জায়গা।😂,0,celebrity
বলার কিছু নাই shame shame shame....,0,celebrity
কিয়েক্টা অবস্থা! সেইইইই কখন থেকে কমেন্ট পড়তেছি শেষই হয়না! ধুরু! যত নাস্তা নিয়ে বসেছিলাম সব শেষ! এত কষ্ট করে যে ১০ কেজি কমাইছিলাম! আপনার পোস্টের কমেন্ট পড়ার সময় যে হারে   খাইসি!  সব টাকাও শেষ! কিয়াক্টা অবস্থা বলেন তো!!,0,celebrity
"মৃত মানুষের সম্পর্কে বাজে কিছু বলতে বা লেখতে নেই,  তাই আমিও আপনাকে  বাজে কিছু বললাম না লেখলাম না 🙂🙂  ওপারে ভাল আছেন তো?",0,celebrity
আপনি সুস্থ হয়ে আমাদের মাঝে ফিরে এসে আবার আমাদের দিক নির্দেশনা দেবেন।,0,celebrity
ট্রস ট্রস করে মারতে হবে। মেরে দালাল কে লাল করতে হবে।,0,celebrity
"মরে নাই,মরে নাই! বাঁইচ্চা রইছে🙈",0,celebrity
"#""২০০১ সালের নির্বাচনে বিএনপি-জামায়াত বিজয়ী হওয়ার পর আমরা অনেকবার এ ধরনের ঘটনা ঘটতে দেখেছি।""  #""এ রকম শুধু একটি ঘটনার খবরই এসেছে;""  আপনারা স্যারকে শুধু শুধু দোষারোপ করছেন। স্যার শুধু এই ইনফো টুকুই দিতে চেয়েছিলেন। মুল বক্তব্য এটাই। এটাই অর্গ্যাজম। বাদবাকি টুকু নিতান্তই ফোরপ্লে... 🐸🐸🐸",0,celebrity
প্রত্যেক পোস্ট শুক্রবারে দেন কেন??? শুক্রবারের পবিত্রতা রক্ষায় মানুষ যাতে কম গালি  দেয় এই জন্যে?,0,celebrity
বাঙ্গালি দাঁত থাকতে দাঁতের মর্ম বুঝে না।,0,celebrity
"একজনের মন ভেঙে গেলে তাকে জোড় করে বেশিদিন বাঁচিয়ে রাখা যায় না,এটা কি সত্য?",0,celebrity
পোস্ট পড়ার সময় নাই কমেন্ট পড়ে বিনোদন নিই😂,0,celebrity
ড জাফর ইকবাল স্যার যে এতো সুন্দর করে গুছিয়ে বিভ্রান্ত সংবাদ ছড়াতে পারে সেটা এই লেখাটা স্পষ্ট। কারণ আপনি কোটা আন্দলনের কোন কিছু দেখেননি এটা সত্য। মতিয়া চৌধুরীর বক্তব্য টা ও দেখেননি কিংবা ঐ সময় পত্রিকা পড়ার সুযোগও পাননি । তাহলে এই লেখা আপনি লিখতেন না। আরও একটা বিষয় পরিষ্কার যে স্বাধীনতা যুদ্ধ আপনি দেখেছেন কিন্তু অংশ নেননি।  ঠিক আজকের এই কোটা আন্দোলন টা আপনি দেখেননি বা শুনেনই নাই। শুধু একটু আঁচ করেছেন মাত্র। সব কিছু জেনে বুঝে কোন কিছু লেখাটা জরুরী। আপনি এমন লেখা লেখার আগে অনেক অধ্যায়ন করবেন। কারণ এটা সত্য যে আজকের ছাত্ররা  আগের চেয়ে অনেক বেশি দক্ষ এবং একটু বেশি সচেতন প্রতিবাদি।,0,celebrity
এইযে আরেক ভন্ড পীরবাবা আসছে মায়াকান্না দেখাতে। বমি করা শেষ নাকি পীরবাবার?,0,celebrity
শিকারী বিড়াল গোঁফে চেনা যায় আর আপনারেও গোঁফে চেনা গেছে,0,celebrity
"""একটা সমস্যা না দেখার ভান করলেইকি সমস্যাটা মিটে যায়?সমস্যা মেটাতে চাইলে সেটাকে সবারআগে স্বীকার করতে হয়। দেশের সর্বোচ্চমহল এই সমস্যাটা স্বীকার করতেই রাজি না।তাহলে সমস্যাটা সমাধান হবে কেমন করে?""  কেউ কি আমাকে বলবেন?",0,celebrity
ফাঁসি দিয়ে দিয়ে আপনাদের দাবী অনুযায়ী যাদের গলায় রশির চাপ দেয়া হয়েছিল তারা কতোটা কষ্ট পেয়ে চাঁদের এ সুন্দর দুনিয়া ছেড়েগেছে তাদের প্রাণ ত্যাগের নির্মম কষ্টটা এবার একটু উপলদ্ধি করুন।  আপনার এবং সকলের কষ্ট আমাকে দুঃখ দেই।,0,celebrity
সালমান মুক্তাদির এবং আপনার প্রকাশ্যে মারা মারি দেখতে চাই।,0,celebrity
"কে তুমি বৎস, ধরিয়া মৎস, বেচিয়া গঞ্জে, অকুল ও কুঞ্জে, না খাইয়া তাজা, কেনো ভক্ষন করিয়াছো মেয়াদ উত্তীর্ণ গাজা 😂😂",0,celebrity
Yes.,0,celebrity
"প্রটোকল ছাড়া বের হইয়েন না রাস্তায় সার, দেশের লক্ষ লক্ষ ছাত্রছাত্রী হড় হড় করে বমি করে দেবে আপনার গায়ে ...(চেতনার ফেরিওলা💩💩)",0,celebrity
"কে তুমি বৎস, ধরিয়া মৎস, বেচিয়া গঞ্জে, অকুল ও কুঞ্জে, না খাইয়া তাজা, কেনো ভক্ষন করিয়াছো মেয়াদ উত্তীর্ণ গাজা 😒😒😒",0,celebrity
স্যার আপনি একজন চরম রাজাকার। ঢাকার পাবলিক টয়লেটের সব মল আপনার জন্য।,0,celebrity
কমেন্ট পড়।অনেক সাহসী আন্দোলনকারী পাবি।   Anjuman Ara,0,celebrity
"তাকে নিয়ে আলোচনার কি আছে? তাকে কি কেউ গুনে না পুছে? একাত্তরে তিনি চুল কাটেন নীলক্ষেতে, কিন্তু যুদ্ধে যান নাই। তার যখন যুদ্ধে যাবার বয়স, তখন সেটা না করে এখন মহান মুক্তিযুদ্ধ নিয়ে বিশাল ব্যবসায়ী বনেছেন। ইগনোর করুন এসকল কপটদের",0,celebrity
আমি এমন ছাত্র দেখেছি যে ইংরেজী উর্চচারন ও ঠিকমত করতে পারেনা। (a+b)   বর্গ কত জানেনা। কিনতু অংকে  A  ইংরেজিতে A  পাইছে।,0,celebrity
"পরম শ্রদ্ধেয় স্যার,  একটা বিষয় বাদে আপনার সব বক্তব্যেই একমত, সেটি হল শহীদুল আলমকে গ্রেফতার করা নিয়ে। দেশের মানুষ এরকমভাবেই সোস্যাল মিডিয়া আর ফেইক নিউজে বিচরণ করতেছে যে একটা প্রতিযোগিতা চলছে, কে কার থেকে কত সুন্দরভাবে রোমহরষক কিছু লেখতে পারবে বলতে পারবে। এটা আইন দিয়ে, পুলিশ দিয়ে কোনভাবেই নিয়ন্ত্রণ করা সম্ভব না। একটা প্রায় পুরোটা শিক্ষিত বোকা জনগোষ্টী আমরা। আবেগ দিয়েই আমাদের নিয়ন্ত্রণ করা যায়,  সেটা সত্য মিথা যাচাই করার সুযোগ পাইনা সময় পাইনা, আরেকটা প্রতিযোগিতা চলে, কে কার আগে আবেগকে কত শৈল্পিকভাবে রঙ তুলি দিয়ে, নিজের সর্বোচ্চ মেধা দিয়ে বিশ্বাসযোগ্য এবং অন্যরকম উপস্থাপনা করতে পারে, যা আর কেউ করতে পারবেনা। এখানে নিয়ন্ত্রণের একমাত্র পথ কঠোর শাসনে রাখা। স্যার আপনি জানেন না, আমরা এমন মেধাবী যে কোন আইন ভাংার আগে সেটা নিয়ে প্রচুর গবেষণা করি!  অপরাধ করার আগে অপরাধী জেনে নেয় ধরা পরলে তার কি শাস্তি হতে পারে আর সেই শাস্তি থেকে বাঁচার কি কি বৈধ অবৈধ রাস্তা আছে। কি কি প্রমাণ থাকলে কত কঠিন শাস্তি হবে সেটা জানে এরা এবং সেসব প্রমাণ না রেখে অপরাধ করে, অথবা অপরাধ করার পরপরই প্রমাণ ধ্বংস করে দেয়।  আপনি আশ্চর্য হবেন জেনে স্যার, সেই প্রমাণ হিসেবে যদি একটা মানুষ হয় তাহলে তারা সেই মানুষটাকেও ধ্বংস করে দেয়।  এত বিচার বিশ্লেষণ করে এবং নিবিড় অধ্যাবসায় নিয়ে এরা প্রত্যেকের যায়গা থেকে একেকটা মহা হয়ে যাচ্ছে,  আমাদের পুলিশ বা রাষ্ট্রীয় যেকোন বাহিনী একটা নতুন প্রযুক্তির সাথে আপডেট হবার আগেই সেটা দিয়ে এদেশের অপরাধীরা অনেক বড় বড় অপরাধ করে প্রমাণের অভাবে গায়ে হাওয়া লাগিয়ে রাজার মত চলছে। শহীদুল আলম এর অপরাধটা এক্ষেত্রে আমি ব্যক্তিগতভাবে নেয়ার পক্ষপাতী না,  ব্যক্তি শহীদুল আলম কি করেছে?  শুধু এই প্রশ্নটাতে সীমাবদ্ধ থাকার পক্ষে আমি না। তার এই এতটুকু ভুল বা অপরাধ জাতির জন্য কতখানি ক্ষতি হয়েছে এদিকদিয়ে বিবেচনার পক্ষপাতী আমি। এই বাচ্চাদের আন্দোলনে যারাই এমন কিছু অপরাধ করেছে,  উষ্কানিমূলক,  বিভ্রান্তিকর কিছু বলেছে - করেছে বা প্রচার করেছে নিজের মূল্যবান মেধা দিয়ে শৈপ্লিক উপস্থাপনায় তাদের সবার এইসব ছোট ছোট অন্যায়ের কারনে এবং তার প্রভাবে ছাত্রদের এই অনিরাপদ সড়ক সংশ্লিষদের বিরুদ্ধে আন্দোলনটা,  ছাত্র বনাম সরকারের বিরুদ্ধে যাচ্ছিল কিভাবে স্যার?   যে যত বড় সেলিব্রেটি তার অপরাধ তত বেশি কারন তার ভুল তথ্যটাই বেশি ছড়ায়। মানুষ বিশ্বাস করে।  তার ভুল তথ্যের জন্য মানুষের ক্ষতি হয় বেশি। এখন মাদকবিরোধী যুদ্ধে যদি একদম শেষ লেবেলের খুচরা মাধ্যমকে দমন করে আর এ ব্যবসার ব্রাদার ফাদার গডফাদার রেখে দেয়া হয় তাহলে ত কয়েক মিনিট পর থেকেই আবার চলতে থাকবে। তেমনি শহীদুল আলমকে গ্রেফতার করায় তার মত বা তার চেয়ে নিচু মানের গুজবগুলা বা অপপ্রচারকারীরা চুপসে গেছে।   আপনি স্যার একজন অসাধারন মানুষ। রাজাকার শব্দটা বলার সময় আপনি এমন ভাবে ঘৃণা প্রকাশ করতে পারেন যে আমি আরো প্রেরণা পাই।  স্যার অনেকদিন ধরে আপনার সাথে কোনভাবেই কোনকিছুতেই দ্বিমত হতে পারছিলাম না,  ব্যাপারটা ভাল না। আবার আপনিও দেখছি সরকারের সাথে প্রায় দ্বিমত হতে পারছিলেন না।  আমি বিশ্বাস করি স্যার,  অনেকদিন কোন বিষয়ে একমত না হওয়া মানে কেউ একজন অপরজনের কাছে মরে গেছে, তার নিজস্বতা নাই,  হোক ঠিক হোক বেঠিক অন্তত কিছুটা অমিল থাকার দরকার।  আপনার জন্য অনেক শুভকামনা স্যার।  আপনি ভাল থাকলে আমাদেরও ভাল লাগে।  শুধু শ্রদ্ধাই করি না,  ভালওবাসি আপনাকে।",0,celebrity
"এই বনে এত ফুল আগে ফোটে নি  এক সাথে এত পাখি গেয়ে ওঠেনি... আহারে নন্দনাল...আপনার লেখাটা পড়ে কবিতাটা মনে পড়ে গেল স্যার..  নন্দনাল তো ১দা করিল ভিষণ পন,  স্বদেশের তরে যে করেই হোক রাখিবে সে জীবন..  সকলে বলিল করকি করকি নন্দনাল,  নন্দ বলিল বসিয়া বসিয়া রহিব কি চিরকাল...  সকলের সাথে সমস্বরে আমিও বলিলাম ভ্যালারে নন্দ, বেচে থাক চিরকাল |",0,celebrity
মুক্তিযোদ্ধাদের পক্ষে লেইখা সিমপ্যাথী কামাইতে চাইসিলেন?,0,celebrity
দায়সারা লেখা..,0,celebrity
"মুহম্মদ জাফর ইকবাল বাংলাদেশী বিজ্ঞানী এবং লেখক মুহম্মদ জাফর ইকবাল (জন্ম: ২৩ ডিসেম্বর ১৯৫২ - মৃত্যু: ২৯ জুলাই ২০১৮) (মৃত্যুর কারণ--এক্সপ্রেশন ত্রুটি: অযাচিত < অপারেটর।–এক্সপ্রেশন ত্রুটি: অপরিচিত বিরামচিহ্ন অক্ষর ""{""।এক্সপ্রেশন ত্রুটি: অপরিচিত বিরামচিহ্ন অক্ষর ""{""। বছর) বিমানবন্দর সড়ক, ঢাকা, বাংলাদেশ।  -উইকিপিডিয়া থেকে।",0,celebrity
এত রাতে পোস্ট করে তারে পোলাপান ঘুমাতে দিচ্ছেনা। কি সেলিব্রেট,0,celebrity
লিখতে পারছেন না কেন স্যার চেতনায় লাগাবে,0,celebrity
কমেন্ট পড়তে আসছি😌😗,0,celebrity
এগুলো হচ্ছে!সবাই স্যারকে একা পেয়ে ধুলাই দিচ্ছে ক্যারে😂😂স্যার ত হার্ট এট্যাক করবো,0,celebrity
ফ দিয়া গেলাম.....বিস্কুট চানাচুর কিনতে দোকানে যাচ্ছি.....খাবো আর পড়বো....বিষম খাবো আর পড়বো....,0,celebrity
গর্তযোদ্ধা,0,celebrity
অনেক ভালো একটা লেখা।,0,celebrity
@ সুভা আজ শহিদ মিনারে যাও নায়?,0,celebrity
স্যার প্লিজ এরকম কথা বলবেন না।আমাদের কথা একটু চিন্তা করে দেখুন।আর কেউ স্যারকে অশালীন মন্তব্য কর না।তোমরা স্যারের পায়ের নখেরও যোগ্য নও।স্যারের প্রস্তাব পছন্দ না হলে ভদ্র ভাবে বল কিন্তু এরকম অ্যাবিউস কর না।,0,celebrity
আপনি ত রাষ্ট্রের ফেছন থেকে চুরি মারা মহান ব্যক্তি।,0,celebrity
বাংলাদেশ এ পি এইচ ডি? স্রিজনশিল পদ্ধতিতে কি আর পি এইচ ডি করা যায় রে পাগলা।,0,celebrity
"আপনার উপর হামলা হলে হাজার হাজার শিক্ষার্থী এক হয়ে আপনাকে বাঁচানোর জন্য আপনার পাশে দাঁড়ায়। আর এখন ক্ষুদ্র ক্ষুদ্র শিক্ষার্থীদের পাশে আপনি নাই। আপনার কাছ থেকে এটা আশা করি নি। আপনাকে 'এককালে' পথপ্রদর্শক মানতাম। আপনি এত দুর্বল চিত্তের মানুষ ঘরে বসে থাকেন, পথে বের হবেন না। ছি.......",0,celebrity
"আপনাকে যে থাকতেই হবে,  না হলে আমরা হারিয়ে যাবো অমাবশ্যার অন্ধকারে।",0,celebrity
"ইয়াহিয়া খানের সামরিক শাসনামলে ১৯৭০ সনে পাকিস্তানে প্রথম সাধারণ নির্বাচন অনুষ্ঠিত হয় নির্বাচনে ভাষানী-বঙ্গবন্ধুর নেতৃত্বাধীন আওয়ামি মুসলিম লীগ ১৬০ আসন পেয়ে একক সংখ্যাগরিষ্ঠতা লাভ করে। আর তখনকার ক্ষমতাসীন ""পাকিস্তান পিপলস পার্টি"" পায় মাত্র ৮৩ আসন। . তখন ক্ষমতা ধরে রাখার জন্য মরিয়া জেনারেল ইয়াহিয়া খাঁন ও কিন্তু মানুষের সুষ্ঠ ভোটাদিকার হরন করেন নি। উনি চাইলেই নিরস্ত্র বাঙ্গালির পুন মেরে পূর্ব পাকিস্তানের সব গুলা আসন দখল করতে পারতেন।  কিন্তু তিনি তা করেন নি। . আর সেই দেশ স্বাধীন হওয়ার পর এতটাই পুন মারা খাইছি যে নিজের ভোট নিজে দেওয়ার আগেই এলিয়েন আইসা ভোট দিয়া যায়। :-/ :-/ আার আপনে আছেন নববর্ষ নিয়ে?",0,celebrity
কিশোর উপন্যাস😂😂😂😃😂😂,0,celebrity
"মুক্তিযুদ্ধ নিয়ে আপনার লেখা পড়লেও খুব আনন্দ লাগে। খুব সোন্দর যুদ্ধ করছিলেন।         আপনি সাহস করছিলেন বলেই এমন সোনার বাংলা আর সোনার ছাত্রলীগ   পাইছি। ভবিষ্যত নিয়া আসলেই চিন্তা নাই, সব ফকফকা।",0,celebrity
"আপনার জানাজা পড়তে পারি নাই, ইভেন্টে ইন্টারেস্টেড দিয়েছিলাম। কিন্তু জানাজার দিন আমার সকাল থেকেই হড়হড় করে বমি হচ্ছিল তাই কেন্দ্রীয় শহীদ মিনারে আপনার জানাজায় থাকতে পারি নি। আপনার বিদেহী আত্মা যেহেতু পোস্ট দিয়েছে সুতরাং তার কাছে ক্ষমা ছেয়ে নিচ্ছি।  আচ্ছা আত্মা কি হড়হড় করে বমি করতে পারে?",0,celebrity
"হাউয়ার পোলা,সোজা কইলেই পারতি যে মার্কাটা নৌকা।",0,celebrity
"জাফর সাহেব, বমি করা বাদ দিয়ে কমেন্টগুলা গোপনে পড়ে যাবেন প্লিজ? কেউ যেন টের না পায় 🙈🙈🙈🙈",0,celebrity
"আমি জানতাম যে শারিরীক ভাবে প্রতিবন্ধী ( সঠিক ভালো বাংলাটি জানিনা বলে ক্ষমা প্রার্থী) যারা তাঁদের জন্য বাংলাদেশে এখনও সর্বস্তরে সুযোগ অত্যন্ত কম। আশংকাজনক ভাবে তারা সব সুযোগ সুবিধা থেকে বঞ্চিত। তাঁদের অস্তিত্ব টাই ভালো মনে ভালোর জন্য গ্রহনের মন মানসিকতাই তো বাংলাদেশের অধিকাংশের আজও তৈরিই হয় নাই।  শারীরিক ক্ষমতায় যারা সীমা বদ্ধ, তারা যে কতো মেধবী হয়, তারা যে দেশের, সমাজের এমনকি পরিবারের উন্নয়নে বা অর্থনীতিতে কতো বড় ভুমিকা রাখতে পারে তা দেশের বাইরে এসে জেনেছি। আরও জেনেছি এখানকার কলেজে ডিপ্লোমা করতে যেয়ে যে দেশের সর্বক্ষেত্রে ""inclusiveness"" থাকতে হবে। যার অর্থ হোল শারিরীক ভাবে যারা চলা চলে অসমর্থ তাদেরকেও সমাজ বা দেশের প্রতিটি স্তরে, ভবনে, প্রোগ্রামে অংশ গ্রহনের সুবিধা করে দেয়া। আর সেই জন্য তারা যাতে হুয়িল চেয়ার নিয়ে যে কোনও জায়গা বা ভবনে আসতে বা যাতায়াত করতে পারে তার ব্যবস্থা নেয়া বা রাখা। আরও শিখলাম তাদেরকে বোঝা ভাবার কোনও কারণ নাই। সুযোগ পেলে তারা সক্ষম মানুষের চেয়েও অনেক সফল হতে পারে বা করতে পারে। এখানকার বাস, রাস্তা, ভবন থেকে শুরু করে সর্বত্র তাঁদের গাড়ী পার্ক বা হুয়িল চেয়ার চলাচলের উপযোগী করে রাখা আছে। হয়তো এইসব কেই মানবিকতা আর প্রকৃত সভ্যতা বলে যা আমরা কিনা আজও জানিনা। কখনও কখনও জানতেও চাইনা।  অনেক ধন্যবাদ ও শ্রদ্ধা শারিরীক ভাবে যারা ক্ষমতায় আবদ্ধ তাদেরকে এতো সুন্দর অনুষ্ঠানে অংশগ্রহনের সুযোগ করে দেয়ার জন্য। এতো সুন্দর একটি উদ্যোগের সকল আয়োজক ও আপনাদের উত্তরোত্তর সাফল্য ও সুস্বাস্থ্য কামনা করছি।",0,celebrity
আপনার উচিত ছিলো নিরপেক্ষ কথা বলা। একজন সম্মানিত মানুষ হিসেবে আমি মনে করি এটা ঠিক হয় নি।,0,celebrity
"আপনার প্রতি অনেক শ্রদ্ধা ছিল... কিন্তু এখন থেকে আর থাকবে না... বিঃদ্রঃ সবাই ওনার লেখাটাকে seriously নিবেন না, জানেনই তো কিছু দিন আগে উনি মাথায় আঘাত পেয়েছিল 😂😂😂",0,celebrity
"আপনার স্ট্যাটাস এ কমেন্ট করতে রুচিতে বাধে। আপনি শিক্ষক নামের কলংক। ছাত্ররা কিসের ভিত্তিতে এবং কোন ঘটনার পরিপ্রেক্ষিত ছাত্ররা আন্দোলনে নেমেছে, সেটা জেনে মতামত জানালে ভাল হত। না জেনেই হুধাই লাফায় পাগলেরা!!",0,celebrity
ওরে জাফররিয়া পাডার ঘরের পাডা তোর মত বলদের মুখে এসব শুনতে চাইনা!পাডা তুইতো মুক্তিযুদ্ধের সময় ১৯ বছর বয়সী ছিলি তাহলে যুদ্ধ না করে পালিয়ে ছিলি কেনরে পাডা।তোরে পাইলে পাডা মর মত পারাইতাম,0,celebrity
"এই বন্ধ্যা দেশের নিষ্ফলা সন্তানরা যেসব কথাবার্তা বলে বেড়ান , তা দেখে শুনে বিচলিত হবার কোন কারন নেই স্যার। বিবেকহীন ব্যাক্তিত্বহীন মৃত মানুষেরা অন্য কোন গ্রহে চলে যাক। তারা কেন ভুলে যায় পতিত জমি চাষ ছাড়া আগাছার জন্ম দেয়। তারা কোন কাতারের ফসল তারাই বুঝে নিক।। টেনশন করবেন না স্যার, আমরা তাদের শত সহস্র বার ভুল প্রমান করে দেব। কথা দিলাম।",0,celebrity
জাফর স্যার বেচেঁ আছেন!  আলহামদুলিল্লাহ!,0,celebrity
আমি রাজাকার।,0,celebrity
দালাল কোথাকার!,0,celebrity
আবেগে মুত আটকায় রাখতে পারলাম না...😆,0,celebrity
স্যার আপনাকে নিয়ে চিন্তায় পড়ে গেলাম গুজব ছড়ানোর দায়ে আর কারো নাম নেয়ার দায়ে আপনাকেও গ্রেফতার করে ডিম থেরাপি দেয় কিনা সেটা নিয়ে,0,celebrity
জানতে চাওয়া কমেন্টঃ স্যারকে রোজা রাখতে বললে কি আমাকে পুলিশে দেবে??,0,celebrity
মনডা চায় পদ্মা সেতুর একটা পিলার খুইলা তোমার জায়গা মতো দিয়ে দেই কিন্তু সরকার আমাকে বিরোধী দল ভাববে দেখে বাইচা গেলা,0,celebrity
"আমেরিকার সরকার প্রধান হাসিনার মত ব্যংক ডাকাতিতে লিপ্ত হতে পারবেনা, সামরিক অফিসারদের সেনা বাহিনীর কম্পাউনডে খুন করতে পারবে না ক্রস ফায়ারে হত্যা করতে পারবেনা গুম করতে পারবেনা নির্বাচনী কেন্দ্রে বিরুধী দলীয় প্রাথীকে পেঠাতে পারবে না,   এবং এর সব গুলোই আপনার ব্যংক ডাকাত নেত্রী করে থাকে এবং সেই ব্যংক ডাকাত হাসিনাকে আপনি সমর্থন করেন। হাসিনার ডাকাত দলের সদস্য হিসেবে আমেরিকার নির্বাচন অবসারবেশন না করে নিজেদের ডাকাতির প্রয়াশচিতত করেন, দেশের মানুষের শ্রমের ঘামে কষ্টে উপার্জিত টাকা হাসিনা চুরি করা বন্ধ করে দিবে।",0,celebrity
"আশা করি এই লেখা কালকে বাংলাদেশ হত্তেক দিন সহ।।। ১ম আলু,   সহ সবাই প্রজাশ করিবো।।  আর আর কিছু ব্লগার এইটা নিয়া কাটাকাটি করবো। কিছু ফেসবুকার চিল্লা ফাল্লা করবো। আর কিছু অনলাইন পেপার  কমেন্ট সহ নিউজ ছাপাইবো।  কেউ তো ব্লগ লিখবো। বিপক্ষে পক্ষে যুক্তি দিবো।  মনের জাল মিটাইবো কেউ। কেউ সুখ নিবো  ।।। কাল সবাই পেপার কিনে কি করবেন। পেপারের কলাম তো আজ ই  লিক হইয়া গেছে।",0,celebrity
আমি একজন_________ পোস্টের কমেন্টে পড়ছি।  শূন্য স্থানের শব্দটা নিজের দ্বায়িত্বে বসিয়ে নিবেন।,0,celebrity
"আপনার দ্রুত আরোগ্য কামনা করি , সাথে এ ও প্রার্থনা করি...আক্রমণকারী যারা , তাদের শুভ চেতনার উন্মেষ হোক",0,celebrity
এতোদিন পরে আপনার ঘুম ভাঙলো এদিকে পোলাপাইন আপনার গায়েবি জানাজা পড়বে বলে তৈরি হচ্ছে।   (কপি),0,celebrity
"ঘুম থেকে উঠার পর স্বপ্ন দেখলাম ,মৃত্যুর পর মানুষ জেগে উঠে তাও দেখলাম। স্যালুট স্যার ।",0,celebrity
তাইলে ঐটা কার কবর? :'(,0,celebrity
"কমেন্টস গুলা পড়তে বসেছি, আর ভাবি কে বললাম মুড়ি আর চানাচুর নিয়ে আসতে খাইতে খাইতে কমেন্টস গুলা পড়মো😜🤓",0,celebrity
আপনি তো পাঠকের মন্তব্য পড়েন না.. আশা করি এবারো পড়বেন না... লজ্জা রাখার যায়গা পাবেন না....,0,celebrity
স্যার এই সব ফালতু ট্রপিক্স বাদ দিয়ে সাহস করে হাতুড়ি বিষয়ক একটা স্ট্যাটাস দিন এবং সেখানে সাহস করে মামুন আর ছাত্রলীগের কৃতিত্বের কথা বলুন ।  তা না হলে বমি করে দেব কিন্তু আপনার মুখের উপর । কারন আপনার এক পেশে চিন্তা ধারা এই জাতী ধারন করতে অক্ষম । অধিকাংশ মানুষের বদ হজম হচ্ছে আপনাদের দুর্গন্ধময় কথায়  । আমার তো বমির উপক্রম হচ্ছে আবার ও ।,0,celebrity
“ধরি মাছ না ছুঁই পানি” জাতীয় লেখা।,0,celebrity
"দেশের পরিস্থিতি স্বভাবিক .... কোথাও কোন ঝামেলা নেই """" চারদিকে শুধু উন্নয়নের জোয়ার """" আবহাওয়া পূর্বাভাস মোটামুটি সন্তোষজনক .....এখন শুনবেন কৃষি সংবাদ . . স্যার ঘুম ভেঙ্গেছে?",0,celebrity
♡♡♡♡♡,0,celebrity
অভাবের জন্য বেশি দূর লেখাপড়া করা টা হয়ে উঠেনি আমার।এই বিষয় টা খুব কষ্ট কর আমার কাছে।আমারো অনেক ইচ্ছা ছিলো কাধে ক্যামেরা নিয়ে দেশের আনাচে কানাচে ঘুরে বেড়ানোর। এক সময় খুব মন খারাপ লাগে আমার যখন দেখি আমার সাথের বন্ধুরা লেখাপড়া নিয়ে বেস্ত আর আমি পরে আছি আমার পুরোনো জং ধরা চিলেকোঠাই। মনে হচ্ছে এই লেখাটা পড়ার পর মনের গভিরে লুকিয়ে থাকা লেখাপড়া না জানার কষ্ট টা আনেক কমে গেছে। কেনো কমে গেছে তা হয়তো পুরোটা গুছিয়ে বলতে পারবো না তাই লিখলাম না।এখন মনে হচ্ছে কি হতো লেখাপড়া করে? কিছু হ্মমতা লোভিদের সোনার বাংলা নামের ঘুড়ির সুতা হতাম?? নাকি বাবার টাকা দিয়ে কেনা সার্টিফিকেটের মালিক???তারচে বরং আমি মূখ্য হয়েই ভালো আছি।।।।নাইবা হলো স্বপ্ন পুরন তারপরোতো নিজেকে কোরবানের গরুর মত বিকিয়ে দিতে হচ্ছে না।,0,celebrity
"সত্যি বলতে জিহ্বাখানা মুখের মাঝে আটকালে, আর কিছু নয়, সমস্যাটা শুধুই জাফর ইকবালে।",0,celebrity
"এই সুন্দর পৃথিবীটাকে আপনি আপনার লেখায় বহুবার তুলে ধরেছেন।। যা পড়ে বেচে থাকার অনুপ্রেরণা পাই।। প্রতি বছর বইমেলায় আপনাকে দেখতে যাই।।। আপনার বই কিনতে টাকা জমাই।। আপনি ভাল হয়ে ফিরে আসুন এই দোয়া করি। আমীন।।। ফিরে আসলে মানুষকে মানুষ হিসেবে গড়ে উঠার সংগ্রাম শুরু করবনে।। আপনার এই অবস্থা অনেক অমানুষের মুখোশ খুলে দিয়েছে।। আগে যাদের ভাবতাম মানুষ,তারা আসলে প্রচন্ড রকমের সাম্প্রদায়িক অমানুষ।।। আশা করি মানুষের মাঝে এই ভেদাভেদ দূর করতে পারব আমরা।।। আপনার সুস্থ ও দীর্ঘ জীবনের কামনা করি। আমীন।",0,celebrity
"এসব তেনা প্যাঁচায়ে লাভ কি!!  পারলে শিক্ষা ব্যাবস্থা পোলাপান বান্ধব করেন... বছরে ১৪ বার সিলেবাস, কোয়শ্চন প্যাটার্ন পাল্টানো বন্ধ করেন... এক পরীক্ষার দিন আরেক প্রশ্ন দেয়া বন্ধ করেন... এমন অবস্থা মনে হচ্ছে কোচিং বাণিজ্যের কারণে দেশ টা রসাতলে যাচ্ছে!!!  শিক্ষা ব্যাবস্থা ঠিক হলে এগুলা অটোমেটিক ঠিক হবে,আপনার মূল্যবান সময় আর কোচিং এর পেছনে দিতে হবে না।",0,celebrity
আজ যদি একটা সঠিক নিবার্চন হতো তাহলে কি এই সব হতো.তাইলে বলুন দোষটা কার???,0,celebrity
"অসাধারন,,,,,,",0,celebrity
"স্যার, দয়া করে আর একবার বৃষ্টিতে বিঝুন। কথা দিচ্ছি, সমস্ত গ্লানি ধুয়ে যাবে। যদিও এখন শীতের সময় রেইন কোট পড়তে ভুল করবেননা।",0,celebrity
কমেড করতে আসছিলাম 😁,0,celebrity
www.facebook.com/arhasnainbd,0,celebrity
কতদিন পর স্যারের কাছ থেকে একটা অরাজনৈতিক পোস্ট পেলাম...😮😮😮  পড়ে ভাল লাগল...😊😊😊,0,celebrity
আপনি বিষয়টা সম্পর্কে ভাল ভাবে জানেনেই না।ছেলেটা কেন নিজেকে রাজাকার বলল।,0,celebrity
"ইকবাল কাকু, এইটাই আপনার শেষ লেখা যেটা পোলাপান আগ্রহ নিয়া পড়ছে।",0,celebrity
"এক বন্ধুরে কইলাম, দোস্ত জাফর ইকবাল স্যার পোস্ট দিছে।তার পোস্ট টা পইরা ২ মিনিটের মধ্যে আসতেছি।১০ মিনিট পর বন্ধু কল দিলো কই তুই?তখনও আমি জাফর স্যারের পোস্ট পড়তেছি।।।",0,celebrity
কাগু পল্টিবাজি শিখতে চাই😊,0,celebrity
"পড়তে আসলাম স্টাটাস,,,,,, শিরোনাম মৃত্যুর উপত্যকা।।।।এতো দেখছি বমির উপত্যকা।।",0,celebrity
আপনার জঘন্য গোফ দেখলেই আমার বমি আসে এবং করে দিতে ইচ্ছা করে আপনার মুখের উপর 😬😬,0,celebrity
Yes sir! Um w8ing...,0,celebrity
সারের ফিরে অাসাতে অাসুন এক মিনিট নিরবতা পালন করি ।,0,celebrity
দালাল,0,celebrity
"দুর্বল প্রকৃতির মানুষের লেখা পড়তে ভালোলাগে না তাই এড়িয়ে গেলাম।   জানাযায় উপস্হিত হওয়ার খুব ইচ্ছে ছিল। এখন দেখছি এটা সম্ভব না। কারণ, জীবতদের তো জানাযা হয় না",0,celebrity
"আমার ""জন্মদিন"" কেউ যখন জানতে চায়,আমি বলি-'জাফর ইকবালের জন্মদিনের দিন'।তারিখটা আর বলিনা।ক্লাস সেভেন-এ২০০৭সালে,আমি আপনার বই পড়া শুরু করি।বই গুলো থেকেই জানতে পারি আপনাকে।আপনার দিনে আমার জন্ম বলে ভেতর-ভেতর একটা গর্ব অনুভব করি।কিন্তু আপনার উপর আমার প্রচণ্ড ক্ষোভ আছে।লেখক,আপনার জন্ম আমার জন্য-আমাদের জন্য-দেশের জন্য খুব দরকার ছিলো।তাই স্রষতা,পৃথিবীর অন্য কোনও দেশে নয় আমাদের এই দেশে আপনাকে পাঠিছেন।লেখক,আশি বছর নয়,কোনো সংখ্যা আপনার পাশে বসানো যাবেনা ।আপনি লেখক, আপনি অসীম, আপনি পিতা।",0,celebrity
"স্যার,কত বড়ো দালাল হলে সব কিছুতে চেতনার দোহাই দেয়া যায়! শুনছি শিক্ষকতায় আপনার দক্ষতা ভালো,ঐটাই করেন।কলম দিয়ে দালালি করার এই বুদ্ধিজীবীকার ভেলকিবাজি বাদ দেন!!  যেই কলমে চেতনার দালালি করেন,ওই কলম পোলাপাইন পাইলে ..... চেতনাবাজ  শিক্ষক মানুষ আপনি... এতটুকু তো বুঝেন 😄",0,celebrity
"আমাদের দেশ সম্পর্কে এরকমএকটি ভবিষ্যৎবাণী করেছিলেনহেনরী কিসিঞ্জার, যুক্তরাষ্ট্রের সকলপ্রচেষ্টাকে বুড়ো আঙুলদেখিয়ে বাংলাদেশ যখন স্বাধীনহয়ে গেল তখন হেনরী কিসিঞ্জারআমাদের দেশকে ভবিষ্যতেরএকটি তলাবিহীনঝুড়ি আখ্যা দিয়েছিলেন। যুক্তরাষ্ট্রভারতকে খুব সমীহকরে চলে এবং নোবেলবিজয়ী অর্থনীতিবিদ অমর্ত্য সেনঅনেকবার বলেছেন সামাজিক সূচকেরঅনেক দিক দিয়ে বাংলাদেশ এখনভারত থেকে অনেক এগিয়ে আছে!হেনরী কিসিঞ্জার এখন কী এইকথাগুলো জানেন?",0,celebrity
"ধর্মপাল, রামপাল, যদি পাল বংশের উপাধি হয়, তাহলে জাফর ইকবাল কোন বংশের উপাধি??",0,celebrity
আলোকিত মানুষ মুহম্মদ জাফর ইকবাল । এ আলো ছড়াতে হবে সবখানে,0,celebrity
"তাজা খবর তাজা খবর          ⭕একটি সঠিক সিদ্ধান্ত         আপনার জীবন বদলে                     দিতে পারে  ⭕নেটওয়ার্ক মার্কেটিং এর            জগতে এটাই প্রথম বিশ্ব রেকর্ড,🌐বিনা ইনভেস্টমেন্টে আনলিমিটেড ইনকাম। 🌐World এ স্বীকৃত প্রাপ্ত        এবং Google supported এই প্রথম বারের মতো        Champion Network Private Ltd: নিয়ে এলো            বর্তমান সময়ের উন্নত  মার্কেটিং         প্লান।🌻 👉 কোন প্রকার টাকা পয়সা প্রয়োজন নেই,  👉ID খুলুন সম্পূন্য ফ্রি আর ইনকাম করুন আজীবনের জন্য।  👉প্রত্যেকে ID ওপেন করার সাথে সাথে কোম্পানীর পক্ষ থেকে $1 ডলার বোনাস পাবেন  👉বাংলাদেশের টাকা৮২  👉Withdrawal Money Payza, Paypal এবং যে কোন ব্যাংক থেকে টাকা উত্তোলন করতে পারবেন।  ★Joining Process Playstore থেকে Champcash Apps Install করে ওপেন করুন ।  sign up with champcash এ ক্লিক করুন । নাম, ইমেইল, পাসওয়ার্ড, জন্ম তারিখ, মোবাইল নং, দেশের নাম, বিভাগের নাম, জেলার নাম পূরণ করুন । Agree terms & conditions এ ক্লিক করুন । এরপর Proceed দিন। Refer ID এর জায়গায়  👉(16278380)বসিয়ে Submit দিন এর পর Verify করে বুঝে নিন আপনার মেম্বারশিপ। আরো বিস্তারিত জানতে,,,আরো বেশী ইনকাম করতে 👉 inboxকরুন।""""  What's app no-01771471624",0,celebrity
আপনি রাজাকারের সন্তান।।। আপনার বাপকে মুক্তিযোদ্ধারা মেরেছে।।,0,celebrity
"আফসোস, ""হা হা"" একবারের বেশি দিতে পারি না😞",0,celebrity
স্যার কোমা থেকে কবে বের হলেন? এক সময় আপনার অনেক ভক্ত ছিলাম। এখন আপনার কর্ম আমাকে তিক্ত করে তক্তা বানিয়ে দিছে।😁🐮,0,celebrity
"""সেলুট ""আপনার পুরো পরিবার কে",0,celebrity
"স্যার, দালালিকে শিল্পের পর্যায়ে নিয়ে যাওয়ার জন্য আপনার তো শান্তিতে নোবেল পাওয়া উচিত।",0,celebrity
সরকারের সাড়া আছে । তাই ইঁদুর গুলো আস্তে আস্তে গর্ত থেকে বের হয়ে আসছে 😭😭😭,0,celebrity
"আপনি কেম্নে লিখতে পারবেন স্যার? আপনিতো সেই গর্ত খূডা মুক্তি যোদ্ধা,,,তাইনা স্যার!?",0,celebrity
"ধরি মাছ না ছুই পানি ।।।তেমার মত বালের শিক্ষিত আমার দেশে অনেক আছে,,দালাল",0,celebrity
কমেন্ট পড়তে আসছি 😊  এত বিশাল রচনা স্কুলের পরীক্ষায় ও ধৈর্য নিয়ে পড়ি নাই....এখন কেমনে!  😃,0,celebrity
"কিছু কমেন্ট দেখে মনে হয় দেশে পাকিস্তান আর ইন্ডিয়ান চেতনায় ভরে গেছে, তাঁদের কাছে বাঙালি চেতনা দুধ ভাত।",0,celebrity
সবাই জাফর ষা‌ড়ের জন্য মুনাজাত ধ‌রেন,0,celebrity
"বিনয়ের সাথেই বলছি - ""ইংরেজি নববর্ষ"" কথাটাই ভুল। আর সত্যের অপলাপ তো আছেই। বিবেকের জানালায় তালা লাগিয়ে বুদ্ধিজীবী হয় কী করে?   এটাকে বিশাল বিজয় বলতে বিবেক লজ্জা পেলোনা?",0,celebrity
জনাব কি চার দিনের স্পিচ একদিনে দিলেন!!!বেশ👏,0,celebrity
স্যার প্রথমেই আমি মানে বুঝতে পারছি না আপনার লেখায় হাহা রিয়েক্ট করব নাকি এংরি  রিয়েক্ট করব৷ আর আমার মনে হয় আন্দোলনরত ছাত্ররা গণিত অঅলিম্পিয়াডে অংশগ্রহণ করেনি তাই আপনি এত লেট করলেন ।তাই না?,0,celebrity
বিজ্ঞান বিষয়ক অনেক আইডিয়া  মাঝে মধ্যে  আমার মাথায় আসে।আমি এখন কি করব?( ৯ম-১০ম কমার্স ছিল),0,celebrity
মদ  খান মদ। আর Relax থাকেন।😂😂,0,celebrity
ঐদিকে বিশ্ববিদ্যালয়ের শিক্ষার্থীরা মার খাচ্ছে আর শিক্ষক হয়ে চুপ করে বসে আছেন দেখে আমারো আজ আপনার ওপর গলায় আঙ্গুল দিয়ে হড় হড় করে বমি করে দিতে ইচ্ছা করছে স্যার!!!,0,celebrity
হা হা আসছে মিছা শান্তনা দিতে। দালাল,0,celebrity
স্যার ১৯৭১ সালের মুক্তিযোদ্ধারা নামাজ পড়তেন। নামাজের সময় হইছে। আসেন আমরা মসজিদে যাই। নামাজ পড়ে আসি।,0,celebrity
উনি কে?আমি কোথায়?,0,celebrity
আপনাদের  মত দালালদের  জাতী এখন চিনে গেছে ।বাচ্চাদের  সামনে পড়বেন না। গনপিটুনী খেতে পারেন,0,celebrity
আপনি বেচে আছেন স্যার ?,0,celebrity
"আগে আপনার লেখা মনোযোগ দিয়ে পড়তাম, কিন্তু এখন শুধু কমেন্ট পড়ি। ভালই মজা লাগে",0,celebrity
"স্যার আপনার পোস্ট না পড়েই কমেন্ট করতে আসলাম,,,কি কমেন্ট করবো একটু বলে দেন।",0,celebrity
"অভিবাদন..(Asfia Zabin Ringku).আসিফা জেবিন রিংকু,   “আমাদের অভিভাবকদের দ্বায়িত্ব সন্তানদের শুরু থেকেই মাতৃভাষার প্রতি সচেতন করে তোলা”-এ অনুভূতি ভেতরে লালন করার জন্য ।",0,celebrity
"কমেন্টে আপনারা যেসব লিখছেন, উনাকে সামনাসামনি পেলে কি এগুলো বলতে পারবেন?",0,celebrity
স্যার!আপনার কথার সাথে আমি সম্পূর্ণ একমত! চলেন এবার নামাজ পড়ে আসি!,0,celebrity
আবার একটা যুদ্ব চাই সকল রাজাকার আর রাজাকারের বাচচাদের খতম করতে চাই,0,celebrity
কমেন্ট পড়তে আসলাম ।,0,celebrity
"আওয়ামী লীগেও মনোনয়নের জন্য ২০ কোটি চল্লিশ কোটি টাকার চালাচালি হয়, এসব ওপেন সিক্রেট।",0,celebrity
"হেলো জাফর ইকবাল - জ্বী আপনাকে বলছি আমিও স্যার আপনার পুরো কলামটা পড়তে পারলাম না: দুঃখিত। আরে আচ্ছা মানুষ তো আপনি! !! আপনি না সাহিত্যিক?? আমার ডাউট হচ্ছে । প্রতিবাদের ভাষাটাও আপনি বুঝেননি, তাহলে আপনি কিসের সাহিত্যিক?? আমি তো ঢাবিতে সরকারি ছাত্র সংগঠন করি, কিন্তু আমি ও তো আন্দোলনে ছিলাম আমরা হাজারখানেক হিন্দুধর্মের বন্ধু এই আন্দোলনে ছিলো। আমরাও রাজাকার ,????????? স্যার ন্যায্য কথা বলুন ভালবাসা গ্রহণ করুন তেলবাজি বাদ দেন। সাধারণ ছাত্ররাই আপনার জন্যে মাঠে নেমেছিল যখন ছাত্রলীগ আপনাকে পেটানি দিয়েছিল। ও এতো কথা বলছি কেন?? এই মহাজ্ঞানী আবার এই গুলো পড়বে না। একটা কথা মনে পড়ে গেল আজ - যে দেশে মেধার মূল্যায়ন করা হয়না সে দেশে জ্ঞানীজন জন্মায় না, যা থাকে তাহল ইঁদুর; বিড়াল; শিয়াল আর চামচা। ভাল থাকবেন স্যার । হয়তো আমাকে অন্য দেশে পাড়ি জমাতে হবে এই চামচাদের ভীড় থেকে",0,celebrity
মীর জাফর = ১৭৫৭  জাফর ইকবাল = ২০১৮  সময়টা বদলে গেছে তবে জাফরদের কাজ একই আছে......  #পাল্টিবাজ_চাটুকার,0,celebrity
"জি আমি বলবো আপনি না, তুই রাজাকার,,,,",0,celebrity
"এই উল্লুকা পাটঠা,যা হচ্ছে তাকে সাপোরট করে যা নইলে খবর আছে",0,celebrity
আমি রাজাকার। আমি গর্বিত।,0,celebrity
"আমাদের দেশ জিহাদের মতো  অন্ধকারে পরে গেসে,শুধু  আপ্নাদের মতো  গুনিজনেরা পারে এর থেকে বাচা তে।এক্তু চেস্ট। করবেন please,??",0,celebrity
মুক্তিযুদ্ধের সময় আপনার কি কি ভুমিকা তা নিয়ে বিস্তারিত লিখিবেন।  ফিল্টার কি?,0,celebrity
এটা কি জাফর সাহেবের ভেরিফাইড ফেবু পেইজ?  নাকি অন্যকেউ?  এ তো দেখি মজার কারখানা খুলেছেন উনি। বিনুদুনের খনি। আহ এতোদিন মিস হয়েছে আর হবেনা নিয়মিত  খোজ রাখব।,0,celebrity
মাহফুজুর রহমান কোনদিন যে ছাত্রদের সমর্থন দিয়ে ওপেন এয়ারে লাইভ কন্সর্ট শুরু করে দেয় খোদা জানে।😌🐸🌸,0,celebrity
"জীবনে একটা লম্বা সময় আপনি আইডল ছিলেন। আপনার বই পড়েই টেকনোলজির দিকে ঝুঁকে ছিলাম। আপনার বই পড়েই জীবনে অনেক কিছু শিখেছিলাম। তারপর একসময় এসে আবিষ্কার করলাম আপনার বইগুলো ঠিক যতোটা আলোকিত মনে করান আপনি, আপনি নিজে ঠিক ততই অন্ধকারে নিমজ্জিত, কদর্য।   কোটা আন্দোলনের সময়ই আপনার আসল রূপ দেখেছিলাম, এখন দেখলাম আপনি কতটা নির্লজ্জ।",0,celebrity
আপনি নির্লজ্জ নির্লজ্জ নির্লজ্জ! ছি!,0,celebrity
পাব্লিক আপনার কথা আর খাবে না মিঃ হরহর বমি😜,0,celebrity
ওমা আপ্নি বেচে আছেন??😨  পোলাপান তো আপ্নার চল্লিশা করতো আর   কয়দিন গেলে😂  তা জনাব এবার কি হরহর করে বমি করে দেওয়ার ফিলিংস আসেনাই??   খুব জানতে ইচ্ছে হচ্ছে😂,0,celebrity
পুষ্টের চেয়ে কমেন্টে মারত্মক বিনোদন পেলুম😂,0,celebrity
বানান ঠিক রেখে কমেন্ট করার অনুরুধ রইলো...জাতি কিন্তু এখন এই বালের পোস্ট পড়েও দেখে না যাস্ট কমেন্ট পড়তে আসে....জাতি কে বঞ্চিত করবেন না আশা করি.... (২),0,celebrity
"Sir, খুব ভাল লেগেছে।",0,celebrity
এত বড়ো কলাম যে এক লাইন পড়ে আর ধৈর্য কুলালো না😃😃,0,celebrity
স্যার আমার বাসার ছাদের মরিচ গাছে ৪-৫ টা মরিচ ধরসে তাহলে কি আমি স্বাবলম্বীর কাতারে পরি? বি.টি.ভি কে খরব দিলাম আসলোনা😰 আপনি দয়া করে উনাদের নাম্বার টা দিবেন? ফোন করে বেপার টা জানাতাম আমার কষ্ট এর ফল গাছে ধরসে আমি বৃথা জেতে দিব না আপনি স্টুডেন্ট দের সাহায্যে  করতে পারেন নি কারন আপানার শারিরিক বল ছিল না কিন্তু আমাকে তো সাহায্য করতেই পারেন এতে তো আর শক্তি লাগবেনা I_want _justice for my মরিচ😭,0,celebrity
জাফর ইকবালের মতো মীরজাফরদের জন্যই বাংলাদেশ কোনদিন উন্নতি করতে পারবে না। মীরজাফর একটা...😞😞😞,0,celebrity
"আগস্ট মাসে আপনি অশান্তিতে থাকেন।এটা একটা অশুভ মাস!আপনি না কুসংস্কার মানেন না তাহলে একে এত ভয় কেন?যাই হোক, আপনার লাস্ট কয়েকটা লাইন ভালো ছিল।কিছুটা প্রতিবাদমুখর ছিলেন সেজন্য সাধুবাদ। কিন্তু মন থেকে ছিল তো?নাকি আলগা পিরিতি?",0,celebrity
ন্যায় অন্যায়কে একসাথে ধারন করাও একধরনের অপরাধ।একপক্ষে গেছেন বলে মনে হয়নি।,0,celebrity
"স্যার আপনি ঘুমিয়ে পড়ুন, আর উঠবেন না, নাহলে পোলাপাইন আপনার চটোকেশে আগুন লাগিয়ে আপনার গুপ্তধনে দন্ড সেধিয়ে দিবে ঘুম না আসলে ধোলাই পারের মেয়াদ উত্তীর্ণ গাঁজা সেবন করুন। চির নিদ্রায় শায়িত হবেন। রিপ স্যার।😔",0,celebrity
ইন্টারনেট এক্সপ্লোরার  :v,0,celebrity
ওই মিয়া সত্যি করে ক কয়টা ভোট দিসস ?,0,celebrity
মোবাইলের চাজ শেষ আর পরতে পারলামনা,0,celebrity
এইসব কমেন্ট যদি এইলোক পড়ে তাহলে পাগল হওয়া ছাড়া কোন গতি নাই,0,celebrity
"স্যার, আপনার পোস্টে মুতের গন্ধ পাইতেছি, বমি করতে গিয়া আবার মুইতা দ্যাননাইতো?",0,celebrity
স্যার ধন্যবাদ স্ট্যাটাসটি  দেয়ার জন্য।আপনি স্ট্যাটাসটি না দিলে হয়তো কমেন্টগুলো পড়তে পারতাম না।,0,celebrity
"আজ হুমায়ুন আহমেদ বেঁচে থাকলে। হিমু সমগ্রে একটি নতুন গল্প যুক্ত হতো ""হিমু ও চাটুকার জাফর""",0,celebrity
"চাপে পইরা সাধারণত নেতারা মুখ খোলে, তাদের নেতাগীরি বজায় রাখার জন্য। এখন ত দেখি চাপে পইরা দালালরাও এক ই কাজ করে। দালাল-নেতা সব একাকার।",0,celebrity
এভাবে আর চলবে কতকাল?,0,celebrity
লেখাটা পত্রিকায় পড়েছি।  ধন্যবাদ স্যার।,0,celebrity
এখানে আমি রাজাকার শব্দটি মন্ত্রী মতি চৌধুরীর কথা কে ব্যঙ্গ করে লিখা হয়েছে।,0,celebrity
কমেন্টগুলা পড়তেছেন?  🐸   স্যার আমাকে একটু শিখাবেন কিভাবে গর্ত করতে হয় ৷ 🐸,0,celebrity
Would anybody please tell me how can I work with my 10 billion neuron? I thought that it can be possible through practice but again I thought that there can be some other ways to make them work spontaniously. Can you share your idea please...,0,celebrity
"আমার সোনার বাংলা, আমি তোমায় অনেক অনেক অনেক ভালোবাসি।",0,celebrity
স্যার বঙ্গবন্ধু স্যাটেলাইট থাকার পরও আপনি এতোদিন পর নিউজটা জানলেন?  বিদায় পি T বি,0,celebrity
এই শোকের দিনে মাঝ রাতে এক  ডাইনি বুড়ির নেতৃত্বে একদল হায়েনার ঊল্লাস দেখতে হল। এর কি কোন প্রতিকার নেই---।,0,celebrity
আপনার পোস্টে কমেন্ট করার জন্য ঘরে বউ রেখে শালীর ঘরে আসছি মোবাইল চার্জ দিতে,0,celebrity
অনেক ভাল একটি লেখা । ধন্যবাদ ।,0,celebrity
আমি শুধু কমেন্ট পড়তে আসছি........😅😅😅😅😅😅😅😅😅😅😅😅😅😅😅,0,celebrity
"স্যারের লিখা আমার ভাল লাগে না।  ওনার সাথে আমার কোন শত্রুতা নেই, আমার সাথেও ওনার কোন শত্রুতা নেই। তারপরও কেন জানি খুব পিটাইতে ইচ্ছা করছে 😟",0,celebrity
"একজন অপরাধীর ফাঁসি হলে যাদের বুকে যন্ত্রনা হয় তারা যখন  আজ এত পোড়া লাস দেখছে তখন কিনা  নিঃশব্দে নিরবে ডুগডুগি বাজাইতেছে।হাইরে মানুষ, মানুষের প্রতি মায়া নাই, মায়া শুধু দলের প্রতি।ইসলাম কি এই কথাই বলে???",0,celebrity
ছাগকূলের ম্যাৎকার দেখতে আসলাম..... 😂,0,celebrity
"Very sad sir, আপনার কাছ থেকে এইটা আসা করিনি...... কারন সে একটা নাস্তিক, ইসলাম ধর্ম নিয়ে কঠাক্ষ করেছে, আপনি তা ভালো করে যানেন।",0,celebrity
"এদেশে দুটি দল আছে যারা মুক্তিযুদ্ধেই বিশ্বাস করেনা।তাই তাদের কাছে মুক্তিযুদ্ধের আদর্শে দেশ গড়া কথাটা বলা আর গাধার সামনে বীন বাজানো সমান কথা।সে দলগুলোর জন্মের ইতিহাসই ছিল ত্রুটিপূর্ণ তাই তারা বাংলাদেশকে দালালের দেশে পরিনত করেছিল এবং মুক্তিযুদ্ধের আদর্শ অনুভুতিকে তারা ভুলন্ঠিত করেছিল এবং শয়তানগুলোর গাড়ীতে জাতীয় পতাকা তুলে দিয়েছিল।আর এজন্যই তাদের দল দুটির আজ এই জঘন্য অবস্হা।যাদের জন্মের ইতিহাসই ত্রুটিপূর্ণ, জনগন থেকে বিচ্ছিন্ন, গনমানুষের উন্নয়নে যাদের গত দশ বছরে কোনো অবদান নেই,শুধু আছে সন্ত্রাসী কর্মকান্ডের নোংরা ইতিহাস তারা আবার ফাও ফাও ক্ষমতায় যাবার দিবাস্বপ্ন দেখে।জনগনকে তারা এতো বোকা ভাবে,চিন্তা করলে হাসি পায়।",0,celebrity
প্রথম আলো' ২০০৭ সালে গোল্ডেন এ+ কথাটি চালু করেছিল ।,0,celebrity
এটাও কি বিদেশি কোন গল্প থেকে নকল করা?এত সুন্দর লেখা তো জাফর ইকবাল লিখতে পারেন না।😭,0,celebrity
ইকবাল স্যারকে একদিন এইসব কমেন্ট বক্স দেখানোর খুব ইচ্ছা আছে। কেন এদেশের মানুষ উন্নতি করে না একটু হলেও বুঝবে.. 😂,0,celebrity
স্যার অাপনি সত্যর পক্ষে লিখে যাবেন। আপনার প্রতি অগাধ ভালবাসা। মুক্তিযুদ্ধের পক্ষের শক্তি সবসময় আপনার সঙ্গী হয়ে থাকবে। 😍😍😍,0,celebrity
ওর বাচ্চা ছেলে মেয়েরা কেন ক্ষমা করবে? এটা কি ক্ষমা করার মতো ঘটনা?,0,celebrity
ওকে বলো পাগলখানায় যেতে,0,celebrity
"কে তুমি বৎস, ধরিয়া মৎস, বেচিয়া গঞ্জে, অকুল ও কুঞ্জে, না খাইয়া তাজা, কেনো ভক্ষন করিয়াছো মেয়াদ উত্তীর্ণ গাজা 😂😂",0,celebrity
"আপনি আমার প্রিয় লেখক না। আমার প্রিয় লেখকের ছোট ভাই, সেই হিসেবে আপনাকে জানাই শুভ জন্মদিন।।",0,celebrity
এই পৃথিবীতে মা নাই যার তার আপন বলতে আর কেউ থাকেনা।প্রতি অক্ষর পড়তে যেন চোখে জল এসে যায়।মা হারানোর ব্যথা সকলের জীবনে আসবে,0,celebrity
আবার একটি গর্তের কাহিনি,0,celebrity
"আমাদের যুগের মা আর এ যুগের মা! এত দূরত্ব  কল্পনা করা যায় না। আয়েশা ফয়েজ একজন মুক্তিযুদ্ধের  শহীদ এর সহধর্মিনী,নিজের মা এর কথা এবং অতীত দিনের বাস্তব ঘটনাবলী সহজ লেখার মাধ্যমে স্পশ করেছে মন ঝরছে চোখের পানি। আমাদের,সন্তানদের চোখের পানিতে মা  এরা জান্নাত বাসীনি হবেন। আমিন।",0,celebrity
"স্যার আপনার এবারের কলাম কি হবে  ""তোমরা যারা আন্দোলন করো""",0,celebrity
"এখন সাধারণ ছাত্রদের উপর পুলিশ ও ছাত্রলীগ যে অমানবিক,  বর্বর অত্যাচার করছে সে সম্পর্কে কিছু বলবেন কি?? । নাকি এতে আপনার এলার্জি???",0,celebrity
মীর জাফর ইকবাল স্যার। আজ কোথায় গেল মুক্তিযোদ্ধের চেতনার কথা? মানুষের ভোট ডাকাতি করে চেতনার ফেরিওয়ালারাই ইতিহাসের আস্তাকোড়ে যাবে। এটা শুধু সময়ের ব্যায়াপার।,0,celebrity
"স্যার আপনার প্রতিটা কথার সাথে একমত। এই দেশের রাজাকারেরা আপনাকে দাম দেয়নি, নব্য রাজাকারেরাও দিবে না। আপনি আপনার পথে চলুন। সাথে আছি। ভালোবাসা।💜 (এই কমেন্টস  একমাত্র পজেটিভ কমেন্ট করে সারা বাংলাদেশের মানুষ থেকে ব্যতিক্রম হওয়ার লোভ সামলাতে পারলাম না)😃",0,celebrity
মাছের মায়ের পুত্রশোক। ৫ দিন পরে আইছে ফাকিং চেতনা নিয়া,0,celebrity
"আপনার মুখে অন্তত এসব কথা মানায়না। একেবারেই বেমানান। নাস্তিকদের লেখায় শুধু বানোয়াট, মিথ্যে কল্পকাহিনী-ই মানায়। এসব ইতিহাস একদমই না। আর দালালী করে ভালো পয়সাই হাতিয়ে নিয়েছেন। আরো হাতানোর ধান্দায়.....!",0,celebrity
তোমায় ট্রস ট্রস করে মারা উচিত,0,celebrity
"এতোকিছু উগরালেন!  এতোবড় দেশপ্রেমী, পারলে অান্দোলনে নামেন ;  মানুষের চোখে ভালো হতে হলে, ভালোকিছু করে দেখাতে হয়! 👍",0,celebrity
"""মা"" শব্দটা বলতে,শুনতে,লিখতে বা পড়তে যে অনুভূতিরর সৃষ্টি হয়,তার মধুরতা প্রায় সকলেই পেয়ে থাকে।যা পৃথিবীতে জন্মগ্রহণ করে নিজেকে ভাগ্যবান বলার ১ম পরিচ্ছেদ।  কিন্তু এ রকম সাদাসিধে ""মা"" পেলে তাকে অনেক বেশিই ভাগ্যবান মনে হয়।",0,celebrity
যে টগবগে যুবক থাকা অবস্থায় ও যুদ্ধে না যাইয়া কোদাল দিয়ে গর্তে কইরা নিজেকে রক্ষা করায় ব্যস্ত ছিলো তার উপর আমার হাগু দিতে ইচ্ছা করে,0,celebrity
কমেন্ট কারীরা কি যে কমেন্ট করেন খুব লজ্জা লাগে...হেতে যে বাঁচি আছে তার জন্য সবাই মোনাজাত ধরেন...,0,celebrity
কমেন্ট পড়ে মজা নাও😂😂 Reazul Islam Md Mehedi Hassan Badhon Sâ Kîß Hõqûë JU W EL Marganul Farhan Shaitto,0,celebrity
You're time is over  Be ready for journey to hell,0,celebrity
আপনি বেঁচে থাকুন সকলের মাঝে ৷,0,celebrity
তাইলে জানাজার কি অইবো!,0,celebrity
. ।  ঊদদু,0,celebrity
বমির বন্যায় তো সব ভেসে যাচ্ছে মনে হয় ।,0,celebrity
"আপনার মতো একচোখা দালাল, কীটকে একসময় পছন্দ করতাম! এটা ভাবতেই অবাক লাগে... দালালি ছাড়েন,লাইনে আসেন।",0,celebrity
আপনার হেড লাইন পড়েই যে মন্তব্য আসতে পারে তা হল- আপনি ফেসবুক ব্যবহার করেন নাকি ফেসবুক আপনাকে ব্যবহার করে? মোবাইল কি আপনি চালান নাকি মোবাইল আপনাকে চালায়? কুত্তায় কি লেজ নাড়ায় নাকি লেজ কুত্তাকে নাড়ায়?,0,celebrity
"দেখেছো স‍্যার কত‍্য লম্বা রচনা লিকেছে, এর জন্যই তো এতদিন সময় লেগেছে ।",0,celebrity
পরকাল সম্পর্কেরর জ্ঞান অজ্ঞ ব্যক্তিরাই কাছেই কেবল নশ্বর পৃথিবীকে অবিশ্বাস্য সুন্দর মনে হবে।,0,celebrity
"#খোলা_চিঠি   #বুবলির_ভাই  ভুল করে যারা ক্ষমা চায় তারা মহৎ হতে পারে, কেবল মহৎ হৃদয়ের মানুষই ভুল করে ক্ষমা চাইতে পারে, আর ক্ষমা করতে পারেও মহৎ মানুষ।তুমি তোমার হৃদয় দিয়ে যদি ভাবো তবে দেখবে এই ""বাংলাদেশ সাধারন ছাত্র অধিকার সংরক্ষণ পরিষদের"" নেতারা কতটা উদার, এরা তোমারই ভাই, আর ভাই সবসময় ভাইয়ের ভালই চায়। তোমার বয়স কম তাই তুমি একটা চক্রের  ফাদে পরে ভুল পথে পা বাড়িয়েছ, আর সেই চক্রের হোতারা নিশ্চয় তোমার পরিচিত বা খুব কাছের যারা তোমার আজকের এই পরিনতির কারন। এই দাগ তোমার সারাজীবনের জন্য একটা ট্রমা হিসেবে থাকবে যদি তুমি জাতির কাছে ক্ষমা চাইতে না পার ।তুমি পারলে লাইভে এসে জাতির কাছে ক্ষমা চাও,আর প্রশ্নফাঁসকারীদের নাম প্রকাশ করে দাও। আমার বিশ্বাস রাজউকের ছাত্র হিসেবে তুমি সেটা পারবে, হয়তো তুমি এতটাও নগন্য ছাত্র নও যতটা তোমার কাছের দুষ্টচক্র আজ তোমায় বাংলাদেশের মানুষের কাছে বানিয়ে দিয়েছে। আমার বিশ্বাস তুমি মেধাবী, হয়তো ঢাবিতে এভাবে প্রথম হবার মতো মেধাবী নও, কিন্তু চাঞ্চ পাবার মতো মেধাবী অবশ্যই।তুমি আবারো প্রমান কর যে তুমি ভুল করেছো একটা চক্রের ফাদে পড়ে কিন্তু তুমি প্রশ্ন না পেয়েও ঢাবিতে চাঞ্চ পেতে পার। আর অবশ্যই তার পূর্বে ক্ষমা চাও তোমার ভুলের কারনে। বাংলাদেশের মানুষ ক্ষমাশীল, তোমায় অবশ্যই ক্ষমা করে দিবে! আর এই তরুণরা তো আরও ক্ষমাশীল, তারা ক্ষমা করে অবশ্যই তোমার আগের ভাবমূর্তি ফেরত পেতে সহযোগিতা করবে, তোমায় আবারো আপন করে নিবে। দেখবে তোমায় নিয়ে ট্রল করা বন্ধ করে দিয়েছে। এভাবেই কেবল তুমি এই ট্রমা থেকে বের হতে পারবে । তা নাহলে বিদেশে কেন, যে দাগ লেপটে গিয়েছে তোমাতে, তুমি কোথাও গিয়ে শান্তি পাবে না সারাজীবন, প্রতি মুহূর্তে তুমি অনুশোচনায় ভুগবে কিন্তু করার কিছু থাকবে না, শুধু নিরবে কাঁদবে শান্তি পাবে না। তাই অভিমান করে বিদেশে যাবার মতো আরেকটা ভুল করো না, যে ভুল করে তুমি আর কখনোই বাংলাদেশের মানুষের মনে জায়গা করে নিতে পারবে না বরং আরও বেশি হাসির পাত্র হবে! আরও বেশি ট্রলের স্বীকার হবে সারাজীবন , সে তুমি যেখানেই থাকো । তাই নগন্য এই আমার পরামর্শ তুমি সৎ সাহস করে জাতির কাছে তোমার অনাকাঙ্ক্ষিত ভুলের জন্য ক্ষমা চাও, প্রশ্নফাঁসকারীদের বিচারের আওতায় আনতে সহযোগিতা করো। বাংলাদেশ অবশ্যই তোমায় ক্ষমা করে আপন করে নিবে। কেননা বাংলাদেশ মহান!  ইতি নগন্য নাগরিক।  পুনশ্চঃ তুমি ক্ষমা চাইলে আমার চিঠিতে তোমার সম্বোধনের জায়গা এডিট করে লিখব ""প্রিয় বুবলির ভাই"" । আপাতত শুধু ""বুবলির ভাই"" ই থাক।",0,celebrity
সৃষ্টিকর্তাকে ধন্যবাদ যে আপনাকে সুস্থ রেখেছেন।,0,celebrity
"কাকা, আপনার বই এখন কেউ পড়ে? আর এত বড় বড় লেকচার দেন যে, মুক্তিযুদ্ধে আপনার ভূমিকা কি ছিল জাতি জানতে চায়।",0,celebrity
"কথা শেষ হলে কোনও একজন নেতা হয়ত এসে আমাকে পরিচয় দিয়ে বলবে,আমি ২০১৮ সালে কোটাবিরোধী আন্দোলন এর বিরোধিতা করেছিলাম, ফেসবুকে কেউ এই আন্দোলন নিয়ে পোস্ট দিলেই সেখানে ""হাহা"" রিয়্যাক্ট দিয়েছিলাম.. আমি তখন তাকে জড়িয়ে ধরে বলবো,""সোনার ছেলে"" (পোস্ট থেকে ভুলে বাদ যাওয়া প্যারাটা সংযোজন করে দেয়ায় অবশ্যই আমি আপনাদের কাছ থেকে লাভ রিয়্যাক্ট আর ধন্যবাদ পাবো😂)  আর,ধন্যবাদ জাফর ইকবাল স্যার আমাকে খুব সুন্দর একটা ছেলেবেলা উপহার দেয়ার জন্য😊 আপনি আমার শুধু প্রিয় লেখক না,প্রিয় মানুষও ছিলেন বটে.. খুব সম্মান করতাম আপনাকে,নিজের আইডল ভাবতাম😊 কিন্তু কোটা আন্দোলন এ আপনি যে রুপ দেখালেন তাতে সম্মান,ভালবাসা টা আর রইলো না😊 আপনার কাছ থেকেই শিখেছিলাম মানুষকে সম্মান করতে,ভালবাসতে তাই আপনাকে অসম্মান করবো না কখনো কিন্তু মনে যেটা ছিল আপনার প্রতি সেটা আর থাকলো না😊 ভাল থাকবেন♥",0,celebrity
"প্রতিটা ভালো কাজের পেছনে কতগুলো ভালোমানুষ সবসময়ই থাকে । কখনো কখনো আমরা তাদের সরাসরি দেখতে পাই না কিন্তু ভালো কাজটা ঠিকই নজরে আসে । ধন্যবাদ স্যার,,, শুভ কামনা❤ ( বি.দ্র:   কারো একটা ভুলের জন্য আমরা তার সব ভালো সৃষ্টিকর্মগুলোকে ভুলে যেতে পারি না,, সো রিপ্লাই বক্সে হানাহানি না করলেই ভালো হয় )",0,celebrity
জামাত শিবির দেশের কোথাও পাদ দিছে যার গন্ধে তিনি গরতো থেকে বের হয়ে আসলেন..কেও আমিন না লিখে যাবেন না,0,celebrity
স্যার আপনার লাইসেন্সটা?,0,celebrity
কমেন্ট গুলোতে বিনোদন ছাড়া কিছুই না...  এত বমি... ওয়াক থু..,0,celebrity
"খোলা প্রশ্ন """"""""""""""""""""'""'''''''' আপনি নিজের লিখাতেই স্বীকার করেছেন, আপনি কারো মেইল ও লিখা পড়েন না। তো আপনি নিজের ভুল ও সার্বিক অবস্থা কেমনে বুঝবেন?  আমার দাদা যুদ্ধ করে মারা গেছে কিন্তু বুদ্ধিজীবী ছিলেন না। তাই তিনি শহীদ কিন্তু শহীদ বুদ্ধিজীবী না। আমার চাচাও মুক্তিযোদ্ধা, তিনি কোন সুবিধা নেন না। আমার বন্ধু আকতার, তার বাবা বীর মুক্তিযোদ্ধা।  তিনি সুবিধা চেয়ে পান না। ২ লক্ষ টাকা চায়। তিনি তাই লিস্টে নাম তুলতে পান না। তিনি মৃত ইদ্রিস কমান্ডারের অধীনে যুদ্ধ করেছে। শাহ আলমের মা, মুক্তিযোদ্ধাদের রান্না করে দিত। সব বাদ দিয়ে সে এই মহান কাজটি করতো জীবনের ঝুঁকি নিয়ে তার কপালে কোন সম্মান জোটেনি।  যুদ্ধে গিয়ে মায়ের শিশু সন্তানের চোখ কানা হইছে। সে নারী সম্মানিত হয়নি। সে কানা সন্তান বেঁচে আছে,মা-ও বেঁচে আছে। কেউ খোঁজ নেয় না ।  কোটায় অনেক অনাচার।  দেশ মেধাহীন হয়ে গেল।  যাই হোক,  কামালপুরের(ময়মনসিংহ) যুদ্ধে সবচেয়ে বেশি ক্ষতিগ্রস্ত পরিবার আমরা। আমার বাবা ৭/৮ বছরের বাচ্চা একাত্তরে জীবনের ঝুঁকি নিয়ে মুক্তিযোদ্ধাদের রসদ সরবারহ করেছে। আপনি  ১৯ বছরের যুবক হয়ে যুদ্ধে যাননি। আমার বড় চাচি বাচ্চা শিশু(মহসীন ভাই) কে রেখে ইজ্জত বাঁচাতে ইন্দিরায় ঝাঁপ দিয়ে মরেছে। পরিবারের ২২ জনের  ১৭ জন শহীদ। আমি কোটা সংস্কারের পক্ষে। আপনি কি আমার উপর বমি করার নৈতিক অধিকার রাখেন??? মতিয়া যখন রাজাকারের বাচ্চা বলে, সরকার যখন আদর্শিক বাংলাদেশী ছেলেগুলোকে বলে শিবির,রাজাকার,; তখন কি আপনার লজ্জা হয়? বঙ্গবীর কাদের সিদ্দিকীকে যখন নব্য রাজাকার বলা হলো তখন কি বমি এসেছিল? আপনাকেও বিসিএস মোটিভেশনাল স্পিকারে ডাকে মুক্তিযুদ্ধের কথা শোনাতে?  কেন? কোন মুক্তিযোদ্ধা নেই দেশে? মারা গেল হামিদুল হক বীর প্রতীক ভালো মটিভেশনাল স্পিকার ছিল তাকে তো কেউ ডাকেনি! কমান্ডার সামাদ সাহেব ভালো কথা বলে। তারা যুদ্ধের লিজেন্ড, আমার চাচাও ভালো বলেন। আর আপনি বলেন বমির কথা।  এসব কারো গায়ে বমি করবেন কি?",0,celebrity
এসো কমেন্ট থেকে শিখি ✌ Sunvi Ahmed Maimuna Bintay Rahman Muhammad Riad Morshed Muhammad Rahat Islam,0,celebrity
"স্যারেরে আমার কুপ বালো লাগে,যকন স্যার মেয়েদের লগে চেল্পি তুলে! আমার যে কি হিংসা হয়। উ আম জি",0,celebrity
কমেন্ট পড়তে আসলাম।,0,celebrity
"মদের সাথে দুধ মিশায় খান,   আর মদের শক্তি বাড়ান😁😁",0,celebrity
%%%,0,celebrity
যিনি আল্লাহ আমাকে আরও কিছুদিন বাচিয়ে রাখার কথা বলেছেন তিনি কিভাবে নাস্তিক?,0,celebrity
স্যার আজকের বাংলার সর্বোচ্চ বিদ্যাপীঠ এর কার্যকলাপ দেখে আপনার কাছে জানতে ইচ্ছা করছে - শিক্ষক এর সংজ্ঞা কি??,0,celebrity
"প্রটেস্টারদের উপর যখন নির্মম নির্যাতন শুরু হয়েছিল ঠিক তখনি দেশীয় চ্যানেল গুলো বাতাবী লেবুর বাম্পার ফলন দেখাতে ব্যস্ত ছিল, যেন জীবনের থেকে বাম্পার ফলনই অধিক গুরুত্বপূর্ণ!  স্যার আমার ক্ষুদ্রজ্ঞান এটাই সার্কুলেশন দেই- মানুষ তখনি অন্যের দ্বারস্থ হয় যখন সে পরাস্ত।  স্যার প্রটেস্টারদের নির্যতনের করুণ দৃশ্য আমাদের দেশীয় চ্যানেল গুলো ভুল করেও প্রদর্শন করেনি; হোক সেটা ভয় কিংবা অন্যকিছু।",0,celebrity
"অধিকার' লাশের তালিকা দিবেনা সরকারের কাছে তাদের আত্মীয় স্বজনের নিরাপত্তার কারণে আচ্ছা এটা না হয় মানলাম, কিন্তু  কোথাও তো লাশের ছবি দেখলাম না কয়েকটা ছাড়া। আর দেখেছি ছাগু পেইজগুলিতে ফটোশপ করা কিছু ছবি। আদিলুর রহমান সাহেব কি কারণে  মিথ্যে বলেছেন আমার জানা নেই, তবে সৎ উদ্দেশ্যে নিশ্চয়ই বলেননি! সত্য কথা বললে যদি আমি নিরপেক্ষতা হারাই, তবে আমার কিছু করার নেই। এই সময়ে নিরপেক্ষ থাকা পাপ।",0,celebrity
"আমি এখন তুসকা খাব আর কমেন্ট পড়ব। কবি বলেছেন, ""তুসকা গরিরের রেড ওয়াইন""😜🍷",0,celebrity
"অভিজিতের এই করুণ পরিণতির জন্য তার ""দায়িত্বজ্ঞানহীন বাকস্বাধীনতায়"" দায়ী। মনে রাখা উচিৎ,,বাকস্বাধীনতা মানেই দায়িত্বহীনতা নয়।",0,celebrity
আপনার কথাগুলা কেন এমন বোগাস লাগে বলবেন? মনে হয় আপনি ঢং করতেসেন.,0,celebrity
"আপনার কিচ্ছু হবেনা, কারণ আপনি তো ইদিনিং চোখে দেখতে পান না, শুনতে পান না,  বলতে পারেন না।  হবে কিভাবে? আপনি হলেন চাটুকর, দালাল,  গরীব।  আপনার রং বদলায় মিনিটে মিনিটে----আপনার বুক ধক করে উঠে,  গা শিউরে উঠে কত কি ফিলিংস আসে।  লজ্জা করেনা বলতে।",0,celebrity
আন্দোলন শেষের পথে! আপ,0,celebrity
"আপনি সজাগ হয়েছেন বটে, তবে কি গঞ্জিকা সেবন করিয়া এতকাল নসিকায় তৈল লাগাইয়া ঘুমাইয়া ছিলেন? নাকি ইয়াবার ট্যাবলেটে আসক্ত হইয়া পঞ্চ রজনী পরে ঘুম থেকে জাগ্রত হইয়া দুঃস্বপ্ন সাধন করিয়াছেন??",0,celebrity
"মন্তব্য শব্দটাকে আমরা গাঁয়ের লোকেরা নঞর্থক অর্থে সবসময় বুঝে থাকি। এখানেও তাই-ই বুঝতে হচ্ছে। আজব! একজন জাফর ইকবাল, যার একেকটা বাক্য এখনো এদেশের কিশোর কিশোরীদের সায়েন্টিস্ট হবার স্বপ্নটাকে দুঃস্বপ্ন না ভেবে বাস্তব ভাবার অবকাশ দেয়, তেমন দ্বিতীয় একজন কে আছে তামাম বাঙ্গালায়?",0,celebrity
অনেকদিন পর ইদুর গর্ত থেকে বেড় হয়েছে।😊😊,0,celebrity
নোয়াখালী বিভাগ চাই 😂😂😂,0,celebrity
"......একজন মানুষের জীবনের সবচেয়ে আনন্দময় সময় হচ্ছে শৈশব, আমরা বুঝে হোক না বুঝে হোক আমাদের শিশুদের শৈশব থেকে সব আনন্দ কেড়ে নিয়েছি।.....দোহাই আপনাদের কাছে, এই দেশের ছেলেমেয়েদের শৈশব থেকে আনন্দটুকু কেড়ে নেবেন না।",0,celebrity
"আপনারা যারা কমেন্ট করতেছেন বা করবেন প্লিজ বানান শুদ্ধ করে লিখবেন,,আমরা যারা কমেন্ট পড়ে মজা নিবো বা নিচ্ছি তাদের যেন কমেন্ট পড়ে হা হা রিয়েক্ট দিতে অসুবিধা না হয়🐸🐸🐸",0,celebrity
"যারা কমেন্ট গুলো লিখতেছেন তাদের উদ্দেশ্যে বলছি,দয়া করে বানান ঠিক করে লিখবেন,যাতে করে আমরা যারা কমেন্ট পড়তে এসেছি তাদের কোনো অসুবিধা না হয়😂😂",0,celebrity
আমি ধর্মান্ধদের যেমন ঘৃণা করি তার চেয়েও বেশি ঘৃণা করি ধর্ম অবমাননাকারী  ও তাদের পক্ষে সাফাই গাওয়া লোকদের।,0,celebrity
"স্যার আপনাকে ভালবাসি, শ্রদ্ধা করি। আপনাদের মত কিছু মানুষ আছে বলেই এখনো হতাশাগ্রস্থ হই না।",0,celebrity
"""গুগলের আগে আমরা সার্চ ইঞ্জিন  নিয়ে কাজ শুরু করেছিলাম, কিন্তু Google এসে আমাদের মার  মার দিয়ে দিলো ৷ আমাদের ফার্স্ট স্টার্টআপটা স্তব্ধ  হয়ে গেলো ৷ "" :-p :-p",0,celebrity
"স্যার ভার্চুয়াল জগতে থাকেন না একদমই সময় নষ্ট তিনি কিছুই জানেন না,খালি পত্রিকা পড়ে,স্যার পোস্টগুলান কি ভূতে দেয়😲😲",0,celebrity
লজ্জিত বিবেক! 😣 😣 লজ্জিত জাতি! 😭😭,0,celebrity
ইনশাল্লাহ!,0,celebrity
আর কত দালালি করবেন!!!,0,celebrity
দালালি কিভাবে করতে হয় স্যার আপনার কাছ থেকে শিখতে হবে😊,0,celebrity
জাফর ইকবাল   নিচের মন্তব্য গুলো একটু পড়েছেন কি? ?  বাংলার জনগন আপনাকে কতটা ভালবাসেরে😁😁😁😁,0,celebrity
আচ্ছা স্যার আপনার নানাওতো রাজাকার। তাহলে দালালিতো আপনার রক্তে না স্যার?,0,celebrity
"না জানলে জেনে নেন। তারপর লিখেন। প্রতি পোস্টেই ন্যাকামি। টিভি দেখি না, ফেসবুক কি জানি না, এখনো দুদু খাই, ভায়োলেন্স দেখলে কলিজায় খিঁচ ধরে",0,celebrity
স্যার এইসব কথা  বলে গালি শুনে কি লাভ! কোচিং সেন্টার গুলোর দালারাও  নামে বেনামে অাপনাকে গালি দেবে! সাথে যোগ হবে রাজাকারের বাচ্চা সহ কিছু গাঞ্জা খাওয়া  অপধার্থের দল! ওই  দলের পূর্বপুরুষদের খোজ করলে (পু)  বুজতে পারবেন তারা কি ছিলো! অাপনার দীর্ঘায়ু কামনা করছি!,0,celebrity
পাডা তুমি কইত্তে বাইর হইলা,0,celebrity
পদার্থবিজ্ঞানীর জয় হোক।,0,celebrity
আজকে যারা আপনাকে গালি দিচ্ছে দুই দিন আগেও কিন্তু আপনার ভক্ত হয়ে বসেছিল যখন আপনি সংস্কারের পক্ষে বললেন । আজও কিন্তু আপনি সংস্কার এর বিপক্ষে স্টেটমেন্ট দেন নি । তাহলে রাগ টা কোথায় ? রাগ হল ওদের বিরুদ্ধে এখন কিছুই বলা যাবে না । উনারা এখন দেশের মা বাপ সেজে বসে আছে ! রাস্তা আটকাবে এটা তো অধিকার । কখনো নিজেকে মুক্তিযুদ্ধের চেতনায় বিশ্বাসী বলবে তো কখনো নিজেদের বলবে রাজাকার । ওদের ইচ্ছা । যখন খুশি তাকে মুক্তিযোদ্ধা বানাবে । কখনো বীরশ্রেষ্ঠ বানাবে ! কিছুদিন পরে স্বাধীনতা সংগ্রামের সর্বাধিনায়কও বানাবে । প্ল্যাকার্ড নিয়ে বসে থাকবে ' আমি রাজাকারের বাচ্চা আমার পিতা শেখ মুজিব ' । যাই করুক ওদের কেও কিছু বলা যাবে না । রাতারাতি আপনি সুবিধাভোগী হয়ে যাবেন !,0,celebrity
স্যার অনেকদিন পর আপনার কোন লেখা পড়ে মনে হলে আপনি পাবলিক সেন্টিমেন্ট ধরতে শিখেছেন।,0,celebrity
কাকু আপনি মরিয়া গিয়াছেন শুনিয়া শিরনি বাটিয়াছিলাম।এখন দেখি জেন্তা। তা জা ই হোক আন্দোলন হইয়া শেষ অ হইয়া জাইতাসে আর আপনি দুমুখো সাপ গর্ত থেকে এখন বাইর হইসেন।লাইফ এ আপনার বই কখন ও পড়িনাই।ইনশাআল্লাহ কোনো দিন পড়ব না।,0,celebrity
মোঃ ইসমাইল হোসেন হাহা কেন দিছস একটু বুঝিয়ে দিবি? জাস্ট জানার আগ্রহ কোন জায়গাটায় তোর মনে হয়েছে লিখাটায় হা হা দেয়া যায়,0,celebrity
"আচ্ছা অন্যান্য পোস্টে দালালির জন্য না হয় তিনি হাহা খেলেন, বিদ্রুপের শিকার হলেন। এই লেখাটা সত্যিকার অর্থে একটা ভাল লেখা। এখানেও এরকম করার কী আছে? দালালি করলেও হাহা, লিগের ক্রিটিসিজম করলেও হাহা।  আসলে আপনারা তার লেখা পড়েও দেখেন না, কিছু সস্তা লাইক পাওয়ার জন্য কিছু গ্রুপ থেকে অন্যের জোক কালেক্ট করে কপিপেস্ট কমেন্ট করে যান।",0,celebrity
বঙ্গবন্ধু কে হত্যার মধ্য দিয়ে যারা বেনিফিশিয়ারী হয়েছে তাদেরও বিচার করতে হবে। যারা খুনিদের দূতাবাসে জব দিয়েছে তারা খুনের নেপথ্যে ছিলো।,0,celebrity
মদ খা মানুষ হ ।,0,celebrity
"জাফর সাড়,মুক্তিযুদ্ধে যাওনি কেন? দালালি ভালোই কর সাড়!",0,celebrity
"@এডমিনঃ দয়া করে উপরের ""Rashed Babu"" গরু টাকে ব্লক করে খোয়ারে পাঠিয়ে দিন তো ...।।",0,celebrity
"এই ভালোবাসাময় পৃথিবীতে এখনও অনেক ভালো মানুষ আছে,আর আছে আপনার প্রিয় ছাত্র ছাত্রীরা,তাদের সবার জন্যই সৃষ্টিকর্তা দ্রুত আপনাকে সুস্থ করে তুলুন।",0,celebrity
এই দেশে সত্যের বিচার খুবই কম হয় কিন্তু স্যার সত্য একদিন বের হয়ে আসবেই আজ শহিদুল আলম বলেছে তাই তাকে এই অবস্থা হতে হয়েছে। কিন্তু বাংলার মাটিতে আর কতজন শহিদুলকে আটকায় রাখতে পারব।।,0,celebrity
এক ঘণ্টা হয়ে গেছে তোমরা কি কর ??? ব্জ্র রোকন Kaium Al Zadid,0,celebrity
"স্যাডকে পুরুস্কার দেয়না কেরে,,,",0,celebrity
স্যারকে মনে হয় গর্ত থেকে সাপে কামড়ে বের করে দিয়েছে  :-P,0,celebrity
বাংলাদেশে ভুয়া মুক্তিযোদ্ধা আসল মুক্তিযোদ্ধা চেয়ে অন্তত ২২৯%। সে বিষয়ে কিছু যদি বলতেন।,0,celebrity
"স্যার কিছুক্ষণ আগে ব্রেকিং নিউজ পেলাম আপনি হার্ডএটেক করে মৃত্যুবরণ করেছেন.."" আর আপনার লাশ দেখতে গিয়েছেন আমাগো অশিক্ষামন্ত্রী🖕  আর এখন দেখি আপনি জিন্দা আছেন এখনো,,,, কেমনে কি স্যার?🤗",0,celebrity
এত ত্যানা না পেচাইয়া বলতে পারতেন নৌকায় ভোট দিন।  তাইলেত লেটা চুকে যায়। আজাইরা কত গুলা লেখা লিখছেন কস্ট করে।,0,celebrity
ওপারে ভালো থাকবেন ষাড়😖😖😖😖,0,celebrity
"আপনি যদি শহিদুল আলমকে নিয়ে এতটাই বিচলত হয়ে থাকেন তাহলে খুব স্বাভাবিক আপনি আল-জাজিরাকে দেয়া উনার সাক্ষাতকার একবার হলেও দেখে নিয়েছেন। আর ফেসবুক লাইভ আপনি বুঝেন না, যেটা শুধু গুগল করে জেনে উচিত ছিলো,  যেহেতু আপনি উনাকে নিয়ে লিখছেন। আমার প্রশ্ন হচ্ছে এগুলা কেন?দেখিনি, শুনিনি ব্লা ব্লা ব্লা।",0,celebrity
মুক্তিযুদ্ধের সময় আপনি মুক্তিযুদ্ধ না করে কি করেছিলেন তা আমরা জানতে চাই। স্যার আমরা ও অনেক কিছুই হয়ত জানি।,0,celebrity
"জাফর স্যার ছিল সবায় হৃদয়ে ,,হায় বেইমান দুনিয়া আজ কমেন্ট দেখে বুঝলাম উনি আজ কোথায় আছে!!!!",0,celebrity
দুর্জ্জন বিদ্যান হলেও পরিত্যাজ্য,0,celebrity
আমি Agree......,0,celebrity
"এমন আশাবাদী মানুষকে, ভারতবাসী হিসাবে অনেক শ্রদ্ধা জানাই।আপনি সুস্থ থাকুন ভালো থাকুন স্যার।",0,celebrity
এই দেশে ভাল মানুষয়ের দাম নাই,0,celebrity
স্যার তাড়াতাড়ি সুস্থ হয়ে যান।,0,celebrity
বুদ্ধিজীবি বুদ্ধি বেচতে আইসে!,0,celebrity
মীর জাফর ও রাজাকার সমার্থক শব্দ। আপনি জাফর এর সাথে মীর লাগিয়ে নিজের নাম লিখবেন।,0,celebrity
"লেখার ধরনটা বলে দিচ্ছে, ইচ্ছের বিরুদ্ধে লেখা; কি প্রয়োজন ছিল;",0,celebrity
"গল্পের নাম ""কাছের দেশ""! আহ... দিলটা জুড়ায়ে গেলো। কাছের দেশ না লেইখা হ্রদয়ের দেশ বা প্রানের দেশ লিখলে আরও ভালো হইতো।",0,celebrity
আপনি আমার পছন্দের একজন লেখক ছিলেন। কিন্তু আপনার দালালি স্বত্তা আর লেখক স্বত্তা এক করতে পারিনা। স্বার্থের জন্য মানুষ কত বড় দালাল হতে পারে তার উৎকৃষ্ট উদাহরণ হলেন অাপনি। আপনার ভাই হুমায়ুন আহমেদ নিখাদ একজন ভাল মানুষ ছিলেন। ব্যক্তিজীবনে তিনি কিছুটা রোমান্টিক ছিলেন কিন্তু আপনার মত লুচু ছিলেন না। তার সিকিভাগ মেধা-নৈতিকতা অাপনি পান নি।,0,celebrity
খুবই সাধারন একটা লেখা !,0,celebrity
আপনি ৭১ যুদ্ধে গেলেন না কেন ??? এখন  সরকারের সহযুগিতে নিয়ে ভাব চোদান কেন  আপনি তো বড় রাজাকার  আপনার কলম মানুষ পড়ে না মানুষ বুঝে আপনি বড় বাটপার,0,celebrity
দালালীর সুস্পষ্ট লক্ষণ পাওয়া যায়  🤔🤔🤔,0,celebrity
"অামি দেখছি কেউ কেউ "" স্যারকে"" উপদেশ দিচ্ছেন!!! উনাকে উপদেশ দিয়ে কোন লাভ অাছে বলে অামার জানা নেই।   "" (কপটতার দরুন) তাদের অন্তর বাঁকা,  অাল্লাহ তাদের বক্রতা বৃদ্ধি করে দেন। তাদের জন্য রয়েছে যন্ত্রণাদদায়ক শাস্তি।"" অাল-কোরঅান।",0,celebrity
সবাই নতুন নতুন কমেন্ট করেন। আগের কপি মারা কমেন্ট গুলা পড়ে মজা পায়না,0,celebrity
আমরা সবাই পরীক্ষার্থী শিক্ষার্থী হতে পারি নি,0,celebrity
দারুন লিখছেন। খুব ভাল।লাগলো sir। এরকম হওয়া উচিত। বাংলাদেশ এর পলিটিকাল দল গুলরভাবা উচিত।,0,celebrity
"স্যার এই প্রশ্নগুলো ভাবিয়ে তুলছিলো,উত্তর পেলাম।।ধন্যবাদ।।",0,celebrity
বিনোদন বক্স পড়েন৷ :D আশরাফুল রকিব Mohammad Robiul H Raihan ফাদ্বীলা রাদ্বীয়া ওয়াসীমা,0,celebrity
সিরিয়াসলি আমি লিখায় ক্লিক করেছি শুধুমাত্র কমেন্টসগুলো পড়ার জন্য!  বিনুদুন আর বিনুদুন!  স্যার আপনি ঘুমান।,0,celebrity
আমরা কি বারবার ইতিহাসককে কলংকিত করছি না!,0,celebrity
কেউ ঠ্যালাঠ্যালি করবেন না....সুন্দর ভাবে লাইনে দাড়ান...সবাই বমি করার সুযোগ পাবেন....এটা সবার অধিকার..কেউ কারো অধিকার নিয়ে টানাহ্যাঁচড়া করবেন না.....😜,0,celebrity
"জাফর ইকবাল সাহেব যখন আহত হলেন তরুণ ছাত্র সমাজ বুক ফুলিয়ে  তার পাশে দাড়াল কিন্তু যখন ছাত্র সমাজ বৈষম্য দূর করার ন্যায্য দাবীর  আন্দোলন শুরু করল তখন তিনি প্রথমে টেকনিক্যাল সমর্থন দিলেও পরে পাল্টি খেলেন । জাফর সাহেব নিজের স্বার্থ দেখলেন কিন্তু তার ভক্ত তরুনদের ন্যায্য অধিকার দেখলেন না ।  জগন্নাথ বিশ্ব বিদ্যালয়ের নাসির স্যার মিষ্টি কথার ভাষণ না দিয়ে সরাসরি আন্দোলনে ছাত্রদের সাথে যোগ দিয়ে প্রয়োজনে  আহত হন । তরুন প্রজন্মের উচিত ভন্ড জাফর ইকবালের অনুসারী না হয়ে নাসির স্যারের মত ছাত্র বান্ধব সাহসী শিক্ষকের  অনুসারী হওয়া ।  জাফর সাহেব সাদা-কে সাদা আর কালো- কে কালো বলার সৎ সাহস রাখেন না । তিনি ক্ষমতাসীন দলের পালস বুজে নিজের অবস্থান প্রকাশ করেন । মুখোশধারী ভন্ডদের ভাষণ মিষ্টি হয় কিন্তু তারা বাস্তব প্রয়োগে বিশ্বাসী নয় । তরুন প্রজন্মকে বলবো, সাদা- কে সাদা আর কালো - কে কালো বলার সৎ সাহস ধরে রাখুন । দূর্নীতি, স্বজন প্রীতি, ঘুষ ,বে- আইনী কাজ থেকে দুরে থাকুন এবং প্রতিরোধ গড়ে তুলুন । নিজেকে যেমন মানুষ হিসেবে মূল্যায়ন দাবী করেন,  অন্যকেও তেমনি মানুষ হিসেবে মূল্যায়ন করুন। সর্বোপরি দেশকে ভালবাসুন  !!!!",0,celebrity
এমন কমেন্ট তো নুছ্রাত ফ্রীয়ার ছবিতেও পড়েনা😂😂,0,celebrity
"আসলে দাবি সব ভুয়া,মেইন কথা হচ্ছে স্যারকে  সরানো।  তবে সত্যি যে স্যারের আর এভাবে খোলামেলা থাকা ঠিক হবে না,পেশাটা ছেড়ে দেবার সময় এসেছে।লীগ হেরে যাওয়া মাত্রই উনার উপর হামলা হবে বলে আমার ধারনা।",0,celebrity
আজ থেকে আপনার লিখা বই বয়কট করলাম।,0,celebrity
দিনটা ভালোই শেষ হল স্যার আপনার পোস্টের কমেন্ট পড়ে!,0,celebrity
"zafar vai ,,, kemon asen?",0,celebrity
আমি  প্রায় ২০-২৫ জনের কমেন্ট  পড়লাম। প্রায় সবার মনে একই খোব। জাফর নাহিদ গংরা   চোরকে বলে চুরি কর মালিককে বলে সজাগ থাক  যে যার আখের গোছাই দেশ শালার জাহান্নামে যাক,0,celebrity
আপনি গালমন্দ খান না কোন কথায়য়!? :3,0,celebrity
ভালো !,0,celebrity
কি ব্রো? একমাস পরে চোখে পড়ল?? Raihanmohammad Abu Raihan,0,celebrity
"বাংলাদেশের অন্য বড় দুইটি আদর্শহীন রাজনৈতিক দল ক্ষমতার জন্যই রাজনীতি করে।  আর যেটুকু উন্নয়ন মূলক কাজ করে সেটা তো টাইম ডিমান্ডিং। আমি রাস্ট্রপ্রধান হইলেই এসব উন্নয়ন কাজ অটো চলত।  জামায়াত তাদের স্বাধীনতাযুদ্ধে প্রশ্নবিদ্ধ ভুমিকা ছাড়া ৭১ পরবর্তী রাজনীতিতে অন্য দুটি দলের জন্য মডেল হতে পারে।  তাদের দলের নেতৃত্বে যারা আছেন তাদের অধিকাংশ শিক্ষিত মানুষ। একজন প্রকৃত রাজনীতিবিদের মুখের ভাষা সবসময় কেমন হতে হয় সেটা মরহুম আব্বাস আলী খান, গোলাম আযম, মাওলানা নিজামী সাহের বিবৃতি শুনলে তা বুঝা যায় (ইউ টিউবে উনাদের রাজনীতির ভাবনার অসংখ্য ভিডিও আছে) ।  তাদের ছাত্র সংগঠন বাংলাদেশের অন্য সকল ছাত্র সংগঠনের জন্য রোল মডেল। এখানে কেউ চাদাবাজি, ক্ষমতাবাজী, লুন্ঠন, ধর্ষন, সন্ত্রাসী কাজের জন্য নেতৃত্বে আসেন না। যদিও রাজনৈতিক প্রতিপক্ষ হিসাবে জামায়াত শিবিরকে ঘায়েল করার জন্য, তাদেরকে সন্ত্রাসী হিসাবে প্রমাণ করার জন্য এদেশের সরকারী পক্ষপাতদুষ্ট মিডিয়া সবসময় তাদের বিপক্ষে সংবাদ প্রচার করে।  জামায়াতের পক্ষ থেকে যারা এযাবৎ কাল এম পি হয়েছেন, তাদের খোজ নিয়ে দেখুন দায়িত্বপালনে দুর্নীতি তাদেরকে স্পর্শ করেনাই, ক্ষমতার প্রভাবে অন্যের উপর জুলুম করেছে এমন অভিযোগ কেউ নিয়ে আসতে পারে না।  ভৌগলিক কারন, মুক্তিযুদ্ধে প্রশ্নবিদ্ধ ভুমিকা আর নামের সাথে ইসলাম -- এইগুলো না থাকলে জামায়াতে এদেশের সবচাইতে জনপ্রিয় দল হতে পারত।  কিন্তু এদেশের মানুষের অতিরিক্ত ইসলাম ফোবিয়ার কাছে জামায়াত কি চায় সেটা পৌছে না।  মানুষ আবেগতাড়িত হয়ে অন্যদুটি দলকে বারবার ক্ষমতায় নিয়ে আসলেও প্রত্যেকেই সেই পুরোনো পথেই হেঁটেছেন। এদেশের মানুষ ও বোকা। রাস্ট্রের কাছে তার কি অধিকার আছে সে সম্পর্কে ধারনা না থাকায় দুটি বড় দলের দুঃশাসন তাদের চিন্তার জগতকে নাড়া দিতে ব্যর্থ হয়েছে।  জামায়াতের উদ্দেশ্য এবং স্বাধীনতা পরবর্তী সময়ে তাদের কার্যক্রম নিঃসন্দেহে বাহবা পাওয়ার মত। তাদের নেতাদের মত ক্লিন ইমেজের রাজনীতিবিদ তৃনমূলে অন্য সংগঠনের নেই। রাজনীতি কোন জামায়াত নেতার পেশা নয়। খোজ নিয়েন প্রত্যেকেই অন্য কোন উপায়ে জীবীকা নির্বাহ করে চলেন।  স্বাধীনতা যুদ্ধের ভুমিকার জন্য জাতির কাছে তাদের দায় স্বীকার করার সুযোগ এখনো আছে। সেটা করে, দল পুনর্গঠনের মাধ্যমে রাজনীতিতে নিজেদের পুনর্বাসন করতে পারলে এদেশের মানুষের প্রকৃত অধিকার তারাই ফিরিয়ে দিতে পারবে।  যদিও আম বাম বিএনপি, জামায়াতের চরিত্রে কালিমা লেপন করেই যাবে, সেটা শুধুমাত্র রাজনৈতিক কারনে।  নিরপেক্ষ দৃষ্টিতে দেখলে অনেকেই মনে মনে গঠনমূলক রাজনৈতিক দল হিসেবে জামায়াতের ভুমিকাকে ভাল ভাবেই দেখেন।",0,celebrity
স্যার আপনি কি বেঁচে আছেন....😩? শুনছিলাম তো আপনি  এইডসে আক্রান্ত হয়ে মারা গেছেন,0,celebrity
"আমি জান্তাম প্রফেসার মানে একজন educated person, but এমন মু্র্খ লোক প্রফেসার হয় এটা আমি নতুন জানলাম।U r a great IGNORANT mr. professor.",0,celebrity
স্যার আপনার একটা লেখায় পড়েছিলাম আপনি পত্র পত্রিকা পড়েন না (সম্ভবত বিটিভি এবং ইমেইল পড়েন) এবং ফেসবুকের কমেন্ট দেখারও সুযোগ পান না। আপনি এই নিউজটা কিভাবে জানলেন কারন আপনি তো থাকেন কল্পবিজ্ঞানের জগতে।  নিউজটা দেখে কি আপনার বমি আসছিল স্যার?,0,celebrity
"যারা হাসতে পারেন না,,,,কমেন্ট গুলো পড়েন,,,,হাসতে হাসতে পাতলা পায়খানা হয়ে যাবে,,,,",0,celebrity
যা বুজলাম আগের আর এখন দুটোয় সার্কাজম পোস্ট ছিল পাবলিক কে খেপিয়ে মজা নিলো স্যার জাফর। 🤣 🤣 🤣,0,celebrity
বুক ভরা ভালবাসা স্যার,0,celebrity
"আপনার এই লেখা থেকে তরুণ প্রজন্ম কি শিখবে আমি জানি না।তবে আপনার যে বয়স হওয়ার সাথে সাথে মতিভ্রমও বেড়ে গেছে সেটা কিন্তু তরুণ প্রজন্ম বুঝে গেছে।স্যার লেখার স্টাইল পাল্টান,বার বার একই লেখা আর ভালো লাগে না।",0,celebrity
এইটা পড়েন Rawnak Zahan,0,celebrity
তুই রাজাকার তুই রাজাকার  আমারে একজনে কইছিলো অনেক আগে :-D,0,celebrity
কবকমমত,0,celebrity
"শেষ মেষ আল্লাহ্ রেই ডাকলেন,,,হি হি হি....",0,celebrity
স্যার আপনি নাকি মইরা গেছেন😱😱,0,celebrity
"বাংলাদেশ এগিয়ে যাচ্ছে, এগিয়ে যাবে। অর্ধেক মানুষই মাথায় কেবল নেতিবাচক ধারনা নিয়ে ঘোরে, তবু এগিয়ে যাবে 🇧🇩 ।",0,celebrity
কারো ঘুম আসলে জাফর ইকবাল স্যার এর পোস্টগুলির কমেন্ট পরলে নিস্চত ঘুম চলে যাবে। যেমনটি আমার ক্ষেত্রে হইছে। 😂,0,celebrity
সাপ 🐍 উঁকি দিছে 😂😂😂😂😂,0,celebrity
স্যার গর্তের মধ্যে অন্যদের পাদের গন্ধে টিকতে না পেরে বের হয়ে হড়হড় করে বমি করে দিলেন।,0,celebrity
এই লেখাটি ফুটবল না বুঝেই লেখা।,0,celebrity
"একটা বইয়ের বিজ্ঞাপনের জন্য এত কথা বলার দরকার ছিল না । যারা আপনার লেখা বই কিনবেন তাঁরা ঠিকই খুঁজে নিয়েই কিনবেন ।  , তবে সময় পেলে আপনার স্টাটাসের সকল কমেন্ট পড়লে মনে হয় কিছু উপলব্ধি করতে পারবেন । অবশ্য সেটারও একটা শর্ত আছে যে আপনি কিছু উপলব্ধি করতে চান কিনা ! বুঝতে না চাইলে কিছুই বুঝা যায় না ।",0,celebrity
স্বাধীনতা আর কোন দেশ যখন কারোকারো বাবা আর স্বামীর সম্পত্তি হয়ে যায় সেদেশে আরো কারো অধিকার থাকেনা।,0,celebrity
"প্রিয় স্যার,আপনাকে সারাটা জীবন জান প্রান দিয়ে ডিফেন্ড করে যাওয়া একটা মানুষ আমি। মানুষ হ্যারি পটারের ""ডাম্বলডোরস আর্মি"" র মত আমাকে ""মুজাই আর্মি"" নাম দিয়ে ফেলছিল। সেই আর্মি আজকে সসম্মানে আপনাকে ডিফেন্ড করার ব্যাজটি খুলে ফেলছি। আমরা আপনাকে ভালোবাসতাম, মুক্তিযুদ্ধকেও ভালোবাসতাম। মুজিবকেও বাসতাম। এখন কাউকে বাসিনা কারন এখন একটু খেতে চাইলে, বাচতে চাইলে,৷ চাকরি চাইলে, রাস্তায় নিরাপদে ফিরতে চাইলে, বেসিক হিউম্যান রাইটস গুলো চাইলে আমরা রক্তাক্ত হই! আর পচে যাওয়া দালালদের মাঝে আপনিও যেদিন নাম লিখিয়ে ফেললেন, সেদিন থেকে আমরা সবাই রাজার মত আমরা সবাই রাজাকার! আপনার লেখা আমাদের হাসির খোরাক ছাড়া এখন কিছুই যোগায় না! বাচ্চাদের বই এর বদলে আপনার লেখা গুলি এখন জোকসের বই এর প্রক্সি দেয়! ভালো থাকুন ও জোকস লিখতে থাকুন। শুভকামনা!",0,celebrity
পাঞ্জাবিটা ধুয়ে দিসিলাম জানাযায় যাবো বলে!! আমি কি জানাযায় যেতে পারবোনা ফ্রান্স!!!,0,celebrity
"আর আসবনা ফিরে,একবার মারা গেলে,এই বাংলার নীড়ে!যেই দেশে চলে কথার যুদ্ধ নীতিবোধ জাদুঘরে,সেই দেশে আর থাকব না প্রভু তুলে নাও তুমি মোরে।",0,celebrity
স্যার আল্লাহ আপনাকে শত আয়ু দিন। আপনাকে বিনম্র শ্রোদ্ধা জানাই স্যার।,0,celebrity
নাহ! এই মানুষ টাকে পাছায় লাথি মেরে বললেও এনি শুনবেন না! মরনের অাগ পর্যন্ত মুক্তিযুদ্ধ নিয়ে ব্যবসা করে যাবেন!,0,celebrity
শেখ হাসিনার ওপর আস্থা রেখে দেশের মানুষ তাঁর দলকে বিশাল একটি বিজয় উপহার দিয়েছে।,0,celebrity
আচ্ছা এই বদমাইশটা কি তার কমেন্ট গুলা পড়েনা নাকি স্ট্যটাস দিয়েই পাব্লিকের ভয়ে পালাই যাই,0,celebrity
"আমি আজ থেকে ৩-৪ বছর আগে থেকে এই অভিজিত, মিজানুর রহমান,আসিফ মহিউদ্দিন,পারভেজ আলমদের ব্লগ পড়ছি।আমি এক লাইনে সাম আপ করে দেই-ওরা পরিপূর্ণ মুক্তমনা নয়,ইসলাম বিদ্বেষী।ওদের ৯০ পারসেন্ট লেখা ইসলামের বিরুদ্ধে।তাহলে বাকি ধর্মগুলা গেল কোথায়?কেউ সেকুলারিজম ও ফ্রি থিংকিং এর ডেফিনেশন চাইলে বলেন, আমি শিখিয়ে দেব। আসলে ওদের নাস্তিকতা হল একটা মুখোশ। এটা মানি ওদের জ্ঞানের চর্চা অনেক।তবে একটা কথা আছে, একজন ঘুমন্ত ব্যাক্তিকে জাগানো যায় কিন্তু যে জেগে ঘুমায় তাকে জাগানো যায় না!...",0,celebrity
"আজ ক্যানো জানি নিজের বিচি দুটো খুজে পাচ্ছি না, নইলে এতোক্ষনে চাপ দিয়ে মরেই যাইতাম -_-",0,celebrity
"মিস্টার জাফর সাহেব, ১৯৭১ সালের সেপ্টেম্বর মাসে আপনি ১৯ বছরের টগবগে যুবক ছিলেন। তাহলে যুদ্ধের মধ্যে আপনি নিজের রিক্স কমাতে নীলক্ষতের সেলুনে চুল কাটাতে গিয়েছিলেন। কি সুখেই না ছিলেন। অথচ- একই সময়ে বাংলার অশিক্ষিত, চাষাভুষা শ্রেনির লোকজন, আমাদের পূর্বপুরুষরা বনে জঙলে পাকিস্তানী হানাদারদের বিরুদ্ধে যুদ্ধে লিপ্ত ছিলো। চুলকাটা তো দূরে থাক কত দিন খেতে পারছে-- সেটা খোজার সময়ও তাদের ছিলো না।। আজকে আপনাদের লেখা ইতিহাস পড়েই আমরা জেনেছি ১০ বছরে বালকও যুদ্ধে ছিল। তাহলে, আপনি কেন যুদ্ধে যাননি?? দেশের দুর্অবস্হার মধ্যে সাজুগুজু করার জন্য খোদ ঢাকা শহরে উপস্থিত ছিলেন। এবং সেটা গর্ব করে বলেও বেড়াচ্ছেন। আজ আপনি যাদের বিরুদ্ধে কলম চালাচ্ছেন - দেশের ওই অবস্থায় একটা ছেলেও সাজুগুজু করার জন্য বসে থাকতো না-- এরাই দেশমাতৃকাকে রক্ষা করে ঝাঁপিয়ে পড়তো - এটা আমার দৃঢ় বিশ্বাস।",0,celebrity
"আচ্ছা আপনি আসলে লেখক নাকি পা চা'টা  দালাল?  একজন লেখক তো এমন হওয়ার কথা না, তার কোনো দল থাকার কথা না স্বাধীন ভাবে দেশের সব পরিস্থিতি নিয়ে লিখবে সে,,   আর যদি দালাল হয় তবে এক পক্ষীয় থাকবে, দালালীর ইনকাম দিয়ে পেট চালানো যায় সম্মান পাওয়া যায় না।।",0,celebrity
আমাদের জোরালো দাবি ছিলো লাইসেন্স এবং ফিটনেসবিহীন গাড়ি বন্ধ করা।আর সরকার শিক্ষাপ্রতিষ্ঠান বন্ধ করে দিলো। তারমানে কি আমাদের শিক্ষাব্যবস্থা লাইসেন্স এবং ফিটনেসবিহীন?,0,celebrity
"¤ শুভ জন্মদিন, স্যার ¤           পরিবারের সবাইকে নিয়ে ভাল থাকুন, সুস্থ থাকুন - এই কামনাই করছি...",0,celebrity
ফ্রেশ হয়ে আস্তাসি পরবো🤔,0,celebrity
ভিদায় পিতীবি 😂,0,celebrity
আপনি মনে হয় মনে মনে আফসুস করেন কেনো মেয়ে হয়ে জন্মগ্রহণ করলাম না।  আর ধর্ষণ সেটা মনে হয় আপনার কাছে পানি ভাত নাকি!,0,celebrity
"অবশেষে আপনি বেচে আছেন, সবাই খুব বলাবলি করছিল আপনি বেচে না থাকায় আন্দোলন প্রান পাচ্ছে না। আপনার দীর্ঘায়ু কামনা করি।  :D",0,celebrity
"আমাদের শিক্ষামন্ত্রী নাহিদ সাহেবের প্রতি সম্মান জানিয়ে বলতেছি,আপনার কথা শুনলে মনে হয় সব  সমস্যা কালকে শেষ হয়ে যাবে কিন্ত কাজের বেলায় আপনি ও আর পাচ- ছয়টা পাগলা মন্ত্রির মতই ঠন ঠন......।।",0,celebrity
রোহিংগা জাফর,0,celebrity
"অাগে অাপনার লেখা পডার জন্য বারান্দায় বসে হাতে কফি নিতাম,  এখন কমেন্ট পডার জন্য পপকন নেই :/",0,celebrity
"কেউ কিছু বলতে চাইলে বলতে পারেন! কারন তাহার লজ্জা, সম্মান, অত্নসম্মানবোধ  নেই। তাই গায়ে লাগার সম্ভবনা নেই।",0,celebrity
""" আমি একচক্ষু হরিণের মত, এই দেশের সবকিছুকে আমি একবার হলেও মুক্তিযুদ্ধের ফিল্টার দিয়ে দেখি।"" তাই তো জয় বাংলা বলে কেউ চাঁদাবাজি, টেন্ডারবাজি, খুন, হত্যা, ধর্ষণ, হামলা, রাহাজানি, ডাকাতি, বিশ্ববিদ্যালয়ের হলে আগুন, পুলিশের সাথে মুখোশ পরে ভিন্নমতাবলম্বীদের বাড়ীতে লুটপাট,  প্রশাসনের সবস্তরে নগ্ন দলীয়করণ, গনতন্ত্রের নামে কুৎসিত স্বৈরতন্ত্রী শাসন প্রতিস্ঠা, জনগণের অধিকার হরণ করলেও আমার কাছে সব ঠিক মনে হয়। আপনি কয়েকজনকে একসাথে বোকা বানাতে পারবেন, কিন্তু সবাইকে একসাথে কখনো বোকা বানানো সম্ভব নয়। এই প্রজন্ম সব কিছু আপনার গল্প-উপন্যাসের মত গেলেনা তারা নিজের বিবেক-বাস্তব বুদ্ধি দিয়ে চিন্তা করতে জানে। হ্যা আমরাও সব জ্বালাও-পোড়াও নাশকতার বিরুদ্ধে, কিন্তু আপনার মতো এক চক্ষু বিশিষ্ট নই।  সেম অন ইউ দালাল!!",0,celebrity
অনেকদিন হলো স্যারের কোন লেখা পাচ্ছি না।,0,celebrity
অপ্রিয় সত্য কথাগুলো তুলে ধরার জন্য আপনাকে ধন্যবাদ.,0,celebrity
20 বছরের একজন টগবগে যুবক যখন যুদ্ধে না গিয়ে গর্তে লুকিয়ে থাকে এবং রাজাখারদের ভয়ে চুল এর কার্টিং ঠিক করে তারকাছ থেকে মুক্তিযদ্ধের গাল গল্প আর তারে বুদ্ধিজীবী ভাবতে আমার ঘৃণা হয়।,0,celebrity
"এত যে আজেবাজে লাইক কমেন্টস;এরা সব পতঙ্গের মত। আলো দেখলে ঝাঁপিয়ে পড়ে, উত্তাপ কম থাকলে আরাম পায় আর উত্তাপ বেড়ে গেলে পুড়ে মরে।",0,celebrity
"""আমি রাজাকার"" বলাতেই মন বিষিয়ে গেল?? 'ব্যঙ্গার্থ' শব্দটা কি মাথা থেকে বের হয়ে গিয়েছিল?  নাকি ইচ্ছে করেই বুঝেও না বুঝার ভান ধরে থাকেন কে জানে! এত বড় একজন বিজ্ঞানী আর উনি নাকি সার্কাজম বোঝে না 😑",0,celebrity
অসাধারণ লিখছেন স্যার ।,0,celebrity
পোস্ট টা দেখে ভেবেছিলাম নতুন বছরের উপহার ধর্ষন নিয়ে কিছু বলবেন😰  কিন্তু না আপনি দেখি তৈল নিয়ে লিখতে বসেছেন!  কোন কোম্পানির তৈল দিয়ে উপরতলা কে খুশি করা যায়?😊 বললে জাতি একটু হলেও উপকৃত হবে🙏  শেখ হাসিনার উপর আস্থা রেখে দেশের মানুষ তাঁর দলকে বিশাল একটি বিজয় উপহার দিয়েছে! বাক্যটিতে আপনি দেশের মানুষ বলতে কি ১৬কোটি মানুষকে বুঝিয়েছেন?,0,celebrity
"সাইকেলে করে যাচ্ছিলাম, পোস্ট দেখার পর হাসতে হাসতে খাদে পড়ে গেলাম  উদ্ধারকর্মীরা আমাকে উদ্ধার করতে এসে তারাও হাসতে হাসতে খাদে পড়ে গেল 😂",0,celebrity
"স্যার একটা অনুরোধ এরপর নিউইয়র্কে যাওয়ার আগে একটা পোস্ট দিবেন। আপনার কাছে ৯০০ পিচ ইয়াবা পাঠাবো নিউইয়র্কে আমার এক ফ্রেন্ডকে দেওয়ার জন্য। যুদ্ধের সময় আপনি যেমন গর্ত খুঁড়ে ৯ মাস লুকিয়ে থেকেছেন, ঠিক তেমনি ৯০০ পিচ ইয়াবা লুকিয়ে রাখবেন। আপনার কষ্ট করে গর্ত করা লাগবে না, ইয়াবা গুলো আপনার পাছার মধ্যে রেখে দিলে হবে। পাকিস্তানি সেনারা, রাজাকাররা যেমন আপনাকে খুঁজে পায়নি, ঠিক তেমনি এয়ারপোর্টের সিকিউরিটিরাও পাছা খুঁজে ইয়াবা পাবে না। বন্ধুকে ইয়াবাগুলো দিয়ে দেবেন। খুশি হয়ে বন্ধু যদি কিছু ডলার দেয় নিয়ে নিবেন। ডলার নিয়ে সেলুনে গিয়ে আপনার শক্ত মোচগুলো কেটে ফেলবেন। আপনাকে দারুন লাগবে। অনেকে অবশ্য বলবে মিসকা শয়তানের মত লাগছে কিন্তু কান দিবেন না।",0,celebrity
পাকি জারজদের গায়ে লেগেছে। তাই পালে পালে গালি দিতে আসছে এইখানে।,0,celebrity
"ভালোর মধ্য খারাপ এই নিয়েই দুনিয়া। মনে সাহস রাখেন, মাবুদের উপর ভরসা থাকলে  অবশ্যই তাড়াতাড়ি ভালো  হয়ে যাবেন",0,celebrity
"জাফর স্যার, আপনি বলেছিলেন মুক্তিযুদ্ধ একটা ফিল্টার। আসলে আপনি নিজেই একটা ফিল্টার। আপনার উপরে কারা ক্ষুব্ধ সেটা দেখে অধুনা জামাত শিবির ও তাদের সমর্থক চেনা যায়। জয় বাংলা, জয় বঙ্গবন্ধু।",0,celebrity
ইশ সবাই আপনার মত করে ভাবলে . . .,0,celebrity
এই প্রথম আপনি গণধর্ষণের কথা শুনে আগের ঘটে যাওয়া সব গনধর্ষণের গ্লানি থেকে আওয়ামীলীগ কে মুক্তি দিলেন...।,0,celebrity
দেরিতে হলেও বিনোদন পাইলাম। এই সাপ্তাহ চলবো??,0,celebrity
"Raz E Qul Islam & Others, স্যারের যা বলার তা বলেছেন, এই পেজে আগে বলেছেন এবং এই পোষ্টের নিউজটাতেও বলেছেন। আমাদের যা কনফিউশান ছিল, তারা স্যারের বক্তব্য থেকে যা বোঝার বুঝে নিয়েছি। আপনাদের বিভিন্ন আজাইরা প্যাচের উত্তর দেয়া ছাড়াও মনে হয় স্যারের অনেক কাজ আছে, দয়া করে নিজের মাথার ভেতরে লাগা জট নিজে খুলুন। আর আপনাদের কেন মনে হচ্ছে স্যারের বাবার খুনীর শাস্তি নিয়ে স্যারের চেয়ে আপনাদের ফিলিংস বেশী, এবং এটা নিয়ে কি করা উচিত সেটা আপনারা বেশী বুঝতে পারছেন?",0,celebrity
এই রকম ঘটনা আরো ঘটবে প্রস্তুত থাকেন লেখার জন্য,0,celebrity
মুক্তি যুদ্ধের সময় আপনি কোথায় ছিলেন ? আপনার লেখা গুলো এক ক্রেন্দ্রিক ..... মুক্তি যুদ্ধের ফেরিওয়ালা ... যারা যুদ্ধের কাহিনী বিক্রি করে খায়,0,celebrity
ওয়ার্ল্ড কাপ নিয়ে লিখাটি প্রশংসার দাবি রাখে। এই লিখার উপর অনেক গুলো কমেন্টেস পড়লাম। ভালো খারাপ দু'টোই আছে ।তবে খারাপ কমেন্টস এর সংখ্যাই বেশি। তাতে মুক্তিযুদ্ধের বিরোধী লোকও থাকবে এটাই স্বাভাবিক। কিন্তু স্যার! এই মূহুর্তে ওয়ার্ল্ড কাপের উন্মাদনা কে উপলক্ষ করে আপনার এই লিখা ? কিন্তু এই দিন দুই আগে ফেসবুকে ঢাকা বিশ্ববিদ্যালয়ে এক ছাত্রীর সম্ভ্রম হানি হলো যা বিশ্ববিদ্যালয় গুলোর ইতিহাসে নজিরবিহীন। স্যার! এই জঘন্য কর্মকান্ড ওয়ার্ল্ড কাপের চেয়ে আপনার দৃষ্টিতে কেন নগন্য মনে হলো ? কমেন্টস গুলোতে সে কথাই বার বার ফিরে এসেছে। তা হলে কি আপনি ইচ্ছে করেই ছাত্রলীগের এমন বর্বরতা দেখেও দু'কথা লিখলেন না ?,0,celebrity
"চ্যার, আপনি সেফায়েত উল্লাহ দাদার শিষ্য হয়ে যান...",0,celebrity
আপু!!!! ই ই ই Mithyla Ferdous,0,celebrity
স্যার সত্য কথা সবসময় বলে যান। এই দেশে অাবার যুদ্ধ করতে হবে বুঝি।,0,celebrity
"স্যার, শুধু টোকাই না, ওখানকার পার্কে বুয়াদের প্রবেশও নিষেধ 😡😡😡",0,celebrity
কোঠা অান্দোলনের মাধ্যমে লোকটার অাসল রূপ এখন সবার কাছে পরিস্কার।,0,celebrity
"জঘন্য লোকটির ""তিনি, করছেন"" এই জাতীয় শব্দগুলো ব্যবহার না করলেই হতো, স্যার!!",0,celebrity
"বাবা মীর মদন, দেখো তোমারে জনতা কিভাবে দিচ্ছে সোদন!",0,celebrity
"অনেক মিস করছি আপনাকে। আজ যদি আপনি বেচেঁ থাকতেন, আপনি নিশ্চই এই কোমলমতি ছাত্রছাত্রীদের পাশে এসে দাঁড়াতেন।  ওপারে ভাল থাকবেন স্যার...  #RIP Sir Mir Jafar Iqbal. 😞  পা চাটা নাস্তিক কু****চ্ছা পশ্চাদপত দিয়ে গরম রড দেওয়া উচিত! মা****দ",0,celebrity
"আমাদের আল্লাহ অসীম দয়াশীল, বাংলা ও বাঙালির সময়ের প্রয়োজনে আপনি আবার প্রানবন্ত হয়ে এই জনপথের মানুষকে আপনার লেখনি দিয়ে সমৃদ্ধ করে তুলবেন।",0,celebrity
অসাধারণ sir.,0,celebrity
"এডমিন ভাইয়েরা, স্যারের লেখাগুলা আর পুস্ট করেন না কেন? ছাগুদের কথায় পুস্ট বন্ধ করলেন?? কি আশ্চর্য!!",0,celebrity
"অব‌শে‌ষে, স্যার কিছু একটা লিখ‌লেন !  অ‌নিচ্ছা‌কৃত হ‌লেও উপায় ছিল না হয়‌তো !",0,celebrity
"একজন মুক্তিযোদ্ধাকে যখন গলায় প্ল্যাকার্ড লাগিয়ে ভিক্ষা করতে দেখি,, তাইলে চিন্তা হয় এই কোটা গুলো কারা পাই।।।।",0,celebrity
"১৯ বছর বয়সে নিশ্চয় আপনার দাড়ি গোফ উঠে গিয়েছিলো।।অথচ আপনার লেখা আমার বন্ধু রাশেদ ১৪ বছরের মুক্তিযোদ্ধা ছিলো।এতদিনে বুঝলাম আপনি অন্তর্গঠনে একরকম বাহ্যিক ভাবে অন্যরকম, একটা মুখোশ পরা ভন্ড।।",0,celebrity
"_নাইচ পোষ্ট! আপনার প্রতিটা লেখার পড়ার জন্যই ফে.বুতে আসি.! অমাবস্যাার চাদের মত আজো আমাদের আশাহত করেননি. দয়া কইরা আমাকে ব্যান দিবেন না তাইলে আমি কি নিয়ে_ বাঁচবো""!!😜😂__",0,celebrity
Wow darun hoyeche,0,celebrity
"ধুর জনাব। আপনার অনেক হেটার জানতাম। কিন্তু আপনি যে নিজেই নিজের হেটার এইটা জানা ছিলো না। শুধুশুধু নিজের রেপুটেশন নষ্ট করলেন। গলায় রাজাকার ঝুলালেই যদি রাজাকার হইতো, তাইলে অনেকেই গলায় মাশরাফি লিখে ঝুলাতো, অনেকেই গলায় নোবেল জয়ী ""ডঃ মোঃ ইউনুস"" লিখে ঝুলাতো, অনেকেই ""লিউনেল মেসি"" লিখে গলায় ঝুলাতো। এখন গলায় তাদের নাম লিখে ঝুলালেই যে সে সেইটা হয়ে যাচ্ছে ব্যাপারটা এমন নয়। এরকম হলে যে পোলাপাইন গুলো মেডিকেলে চান্স পায় নি ওরা সবার আগে গলায় ডাক্তার লিখে ঝুলায়া রাখত।  যে ছেলেটা ""রাজাকার"" লিখে গলায় ঝুলায়া রাখছে ওর মনের ক্ষোভ টা আপনি দেখলেন না। আপনি তো রেগুলার নিউজ দেখেন। আপনি মতিয়া চৌধুরীর ফাউল বক্তব্য শুনেন নি?! নিজের সম্মান নিজেই নষ্ট করছেন স্যার।",0,celebrity
ইসলাম ধর্মে সবচেয়ে খারাপ মানুষ হলো আবু লাহাব আমাদের ধর্মের অনেকে মাত্রাতিরিক্ত বিরক্ত হয়ে একে অপরকে আবু লাহাব বলে গালি দেয় আর এখন আমরা বাঙালী মাত্রাতিরিক্ত বিরক্ত হয়ে একে অপরকে জাফর ইকবাল গালি দেই। খাড়া ফর জাফর ইকবাল✌,0,celebrity
হাইস্যকর 😂,0,celebrity
ততকালীন গর্তবালক আপনি স্যার শুভ কামনা এগিয়ে যান  প্রতিটা কোদাল আপনার সাথে আছে।,0,celebrity
"""কিন্তু""র দোষারোপ করে আবার ""কিন্তু"" দিয়েই জাফর ইকবাল স্যার নিজেই শুরু করলেন দুইনম্বরি কথাবার্তা !....... তারপর অনেকদিন কেটে গেছে, এই দেশে নূতন প্রজন্ম এসেছে, তারা মুক্তিযুদ্ধের কথা শুনে বড় হয়েছে, নিজের দেশের জন্যে তাদের বুক ভরা ভালোবাসা, দেশ নিয়ে তাদের স্বপ্ন, তাদের অহংকার। এই নূতন প্রজন্মের দেশপ্রেমের ভেতর জাফর ইকবাল স্যারদের  কোনো জায়গা নেই। !",0,celebrity
"পাব্লিক ভার্সিটি তে চান্স পাই নাই বলে আম্মু সেই খোঁচান দিছে মন টা খারাপ কমেন্ট দুই একটা পরে দোকান থেকে বাদাম কিনে আনছি  বাদাম খাবো,কমেন্ট পরবো😂",0,celebrity
কমেন্ট পড়তে আসলুম।মধ্যরাতে আর কেউ নাই স্যারের কমেন্ট বক্স ছাড়া।বড্ডCos2,0,celebrity
"কে কেমন সেটা বোঝার জন্য আর আমাদের প্রজেন্মর ছেলে মেয়েদের দালালের দরকার হয়না, তারা আঠারো সালে অনেক রিয়েল এক্সপিরিয়েন্স মেখেছে এবং এখনও মাখামাখি করছে ।",0,celebrity
"সবার চিন্তা ভাবনা যদি আপনার মতো হতো,তবে এই দেশটা এতোদিন অনেক এগিয়ে যেতো",0,celebrity
"ওনি দেখি বেঁচ্চে আছে  , কিভাবে বেঁচ্চে আছে বকলম জাতিকে বকলম মার্কা কিছু উপহার দেবার জন্য। মনে করেছেন আপনাদের মত জাতি এখন বকলম নয়, আপনারা ত সুযোগ সন্ধানী রাষ্ট্রের ফেছন থেকে চুরি মারা মহান ব্যক্তি।",0,celebrity
"অনেক রাত হইছে, তাতে অামার কি? অামিতো কমেন্ট পড়তে অাসছি",0,celebrity
"ওগো স্যার।  অাপনিতো একজন লেখক। নানা মতের, নানা মনের লেখা লিখেন। কখনো মুক্তিযোদ্ধা নিয়ে, কখনো বিজ্ঞান নিয়ে........  অাপনার মত একজন জ্ঞানী মানুষের কেনো যে বুঝতে কষ্ট হয়  "" অামি রাজাকার "" শব্দটা কোন অর্থে বুঝানোর চেষ্টা করছিলো অান্দোলনকারী তরুণেরা।",0,celebrity
বুঝলাম না যেই দেশের মানূষ গুলা গরু থাকতে চায় তাদের পিছে খামাখা মরতেছেন কেন?,0,celebrity
Sir শেষ ভরসা আপনিই।do something for us about the gaps. :(,0,celebrity
ওরা মুক্তিযুদ্ধের চেতনার এত বিরোধী কেন?,0,celebrity
"স্যার,আপনি তাড়াতাড়ি আমাদের মাঝে ফিরে আসুন।",0,celebrity
"অভিজিত্ রায়।বর্তমান সময়ের সব'চে আলোচিত খবর।প্রথমেইবলি এটা একটা নিন্দনীয় ঘটনা।কিন্তু অবাক করার মতবিষয় হচ্ছে কিছুকিছু মুসলিমরুপী মুনাফিক অভিজিত্ রায়ের ধর্মনিয়ে কটুক্তি করাকে মত প্রকাশেরস্বাধীনতা বলে আখ্যা দিতে চাইছে।কিন্তু কেন?মহানআল্লাহ,তার রাসুল (সঃ) এর চেয়ে অভিজিত্ রায়,আসিফমহিউদ্দিনএদেরকেই আপনাদের বেশি আপন মনে হল?যে রাসুলসঃ শাফায়াতকরে আমাদের জান্নাতে নিয়ে যাবেন,যিনি ঐ কঠিনহাশরের সময় ওউম্মতের জন্য সেজদায় পড়ে কাঁদবেন।তাঁকে নিয়ে কেউকুমন্তব্যকরলে কোন মুসলিম কখনোই চুপকরে থাকতে পারেনা,তবে এক্ষেত্রে প্রতিবাদেরভাষাটা ভিন্নহতে পারত;হওয়া উচিত ছিল।আপনি ভিন্নমতে বিশ্বাসী হতে পারেন,কিন্তু ধর্ম নিয়ে এমন মন্তব্যকেনকরা লাগবে যাতে কোটি কোটি মুসলমানের হৃদয়ে আঘাতকরে?মতপ্রকাশের স্বাধীনতা মানেই কি ধর্ম নিয়ে যা ইচ্ছে তাইবলা??",0,celebrity
"আপনাকে কিছু প্রশ্ন করি উত্তর দিবেন ১! আচ্ছা আপনাকে চরিত্রহীন বললে কি আমার নামে মানহানীর মামলা হবে?২! আপনি চেতনার কেজি কত করে বিক্রি করেন? ৩! আচ্ছা গাঞ্জা কি বাজারে কেজি হিসেবে বিক্রি হয়? যা, খেয়ে আপনাকে মাতাল মনে হচ্ছে।",0,celebrity
মেয়াদ ছাড়া গাজা খেয়ে কমেন্ট দেখতে আসছি ষাঁড় চাপর ইকবল 😂😂😂,0,celebrity
জাফর ষাঁড়েরা বেচে থাকুক বছরের পর বছর। নইলে এতো বিনুদন পামু কই!!,0,celebrity
পুরো লেখাটা পড়ে খুব কষ্ট লাগলো যখন দেখলাম আপনি এর সাথে ৭১ এর কোনো কানেকশন পেলেন না 😥 হয়তো পেয়েছেন কিন্তু টাইপিং মিসটেকে ছুটে গেছে। লেখাটা আবার এডিট করার তীব্র দাবী জানাচ্ছি ✌😷,0,celebrity
ড়ঃ কামাল নিশ্চয় আপনার মতো অতিউগ্র চেতনা ধারণ করেন না। তিনি সাচ্চা-নিরেট দেশ প্রেমিক বলেই অজকের এই অবস্থানে।,0,celebrity
"যেদিন থেকে বাঙালিরা- টয়লেটকে 'ওয়াশ রুম' বলতে শিখেছে; সেদিন থেকেই বাঙালিদেরকে 'আধুনিকতার ছোঁয়া' তীব্র ভাবেই আলিঙ্গন করা শুরু করেছে। আর ঠিক সেদিন থেকেই তাঁরা নিজেদেরকে 'সুশীল', 'সভ্য', 'আধুনিক' বলে মনে করে। 😊😉 #Mamun Sj",0,celebrity
কুলাঙ্গারে দেশ ভরে গেছে। পাকি প্রেমিক।,0,celebrity
"নিচের লেখাটি পড়ুন, তারপর নিজেকে সেখানে দাড় করান, ভাবুন নিজের বাবার সাথে এটা হলে আপনি কি করতেন যখন দেখতেন স্বাধীনতার এত বছর পর কেউ বুকে রাজাকার লেখা নিয়ে ঘুরছে। পুরো দুনিয়া দিয়ে দিয়েও যদি কেউ অলংকার-বালাংকার যেভাবেই বোঝাই না কেন  রাজাকার শব্দ কানে কুলাঙ্গারের মত বাজবেই । যদি না বাজে তাহলে সে নিজেই সে কুলাঙ্গারদের তালিকার প্রথম সারিতে থাকবে !!!   # মা কে বিশ্বাস করানোর জন্য সত্যি সত্যি আমি আমার বাবার কবরটা খুঁড়েছিলাম। আমার বাবা পা দুটি ভাজ করে সেখানে শুয়েছিলেন। দশ মাসে তার হাড়গুলি ছাড়া আর কিছুই ছিল নআআ, শুধু তার দুই পায়ে ছিল দুটি মোজা, নাইলনের মোজা বলে এতদিনেও কিছু হয় নি। যখন এই মোজাগুলি পরছিলেন আমি সামনে ছিলাম, এতদিন পরে সেই মোজা পায়ে আমার বাবা কবরের মাঝে শুয়ে আছেন, এই পুরো ব্যপারটাতে কেমন জানি একটা ভয়াবহ কষ্ট লুকিয়ে আছে। আমি খুটিয়ে খুটিয়ে আমার বাবা কে দেখলাম। অনেক কয়টি গুলি লেগেছিল তার শরীরে, অনেকটা আদর করার মত হাত বুলিয়ে দিলাম সেই গুলির আঘাতে। একটি গুলি লেগেছিল মাথায়, কেমন লাগে মানুষের মাথায় গুলি লাগলে??......... তার শরীরের হাড়গুলি একটা একক্টা করে কফিনে সাজিয়ে তুলে আমার মাকে গিয়ে দ্বিতীয়বার তার মৃত্যুসংবাদ দিলাম। একটা গাছের নিচে হাটুতে মুখ গুজে বসে ছিলেন আমার মা। তিনি তখন প্রথমবার তার মৃত স্বামীর জন্য কাদঁলেন। নির্জন একটা নদীতীরে আমার দুঃখী মাকে কাঁদতে দেখে আমার বুকের ভিতরে কিছু একটা গোলমাল হয়ে গেল। আমি ঋষি দুর্বাসা নই, হলে সেদিন ছারখার হয়ে যেত অর্ধেক পৃথিবী।"" ----মুহাম্মদ জাফর ইকবাল---",0,celebrity
আপনি তো রাজনীতি বুঝেন না। তাহলে ইশতেহার বুঝলেন কিভাবে? রহস্যময়! বড়ই রহস্যময়!,0,celebrity
উগ্রবাদী শক্তি  ধ্বংস হোক।,0,celebrity
হুমায়ূন আহমেদ কি তাইলে মিছা কথা কইলো? 😦,0,celebrity
"আমাদের ক্ষমা করবেন স্যার। আপনাকে রক্ষা করার দায়িত্ব আমাদের ছিল, ব্যর্থ হয়েছি। এই দেশটাকে জানোয়ারগুলো শেষ করতে চেষ্টা করছে স্যার। আমরা হয়তো পারছি না জানোয়ারদের আটকাতে। হয়তো আমরা দুর্বল হয়ে পড়েছি।  আপনি, আপনারা থাকুন স্যার, আমাদের সাহস দিন। যতদিন পারি যুদ্ধ চলবে জানোয়ারগুলোর বিরুদ্ধে। আপনার হাসি আমাদের শক্তি দেয়, আপনাদের দেশের প্রতি ভালোবাসা আর বিশ্বাস আমাদের সাহস দেয়। আপনারা সাথে থাকলে আমরা হারবো না। ভালোবাসি স্যার। অনেক অনেক ভালোবাসি আপনাকে।",0,celebrity
উফফফফফ সু হট😂,0,celebrity
স্যার আবার সুস্থভাবে ফিরে আসুন  আমাদের মাঝে।সাম্প্রদায়িক আর মৌলবাদের বিরুদ্ধে কলমের প্রতিবাদ  শুরু হোক।।।,0,celebrity
অতল শ্রদ্ধা আর ভালোবাসা জানবেন স্যার ♥,0,celebrity
"""জিয়াউর রহমানের পাচঁ বছরের শাসনে প্রতি মাঘের শেষে বর্ষন হয়েছিলো কি না তার হিসেব কেউ রাখে নি , তবে এই পাচঁ বছরে কোন প্রাকৃতিক দুর্যোগ হয় নি। অতি বর্ষনে বন্যা না , খরা না , জলোচ্ছাস না। দেশে কাপড়ের অভাব কিছুটা দূর হলো। দ্রব্যমুল্য লাগামছাড়া হলো না। বাংলাদেশের নদীতে প্রচুর ইলিশ ধরা পড়তে লাগলো। বাংলাদেশের মানুষ মনে করতে শুরু করল অনেকদিন পর তারা এমন একজন রাষ্ট্রপ্রধান পেয়েছে যিনি সৎ। নিজের জন্যে কিংবা নিজের আত্মীয়স্বজনের জন্যে টাকাপয়সা লুটপাটের চিন্তা তার মাথায় নেই । বরং তাঁর মাথায় আছে দেশের জন্য চিন্তা। তিনি খাল কেটে দেশ দলাতে চান। জিয়া মানুষটি সৎ ছিলেন , এতে কোন সন্দেহ নেই। লোক দেখানো সৎ না , আসলেই সৎ। তার মৃত্যুর পর দেখা গেল জিয়া পরিবারের কোন ব্যাংক ব্যালেন্সড নেই।"" হুমায়ুন আহমেদ  পৃষ্টা :১৯৩ দেয়াল।",0,celebrity
"ভালো লাগে না,নাই লাগতে পারে,ইগ্নোর করলেই পারে,!বাট খারাব আচরন/কথাবার্তা য় নিজের বংশের/ দেশের  নাম না ডুবালে এদের হয় না!!!এরকম একটা পোস্টে ট্রল করার কি আছে আমি বুঝি না!",0,celebrity
যারা আমার কমেন্ট পরবেন । শুধুমাত্র তাদের জন্যই ৩০০ টাকার এনার্জি বাল্ব ১০০ টাকা ।,0,celebrity
দেশের সবথেকে বড় ঘটনায় অংশগ্রহণ না করে ট্রেঞ্চে লুকিয়ে ছিলেন কেন আপনি!,0,celebrity
"কমেন্ট'স গুলোই বলে দেয় আপনার স্থান  কোথায়,,যুক্তিতর্কে যাওয়ার প্রয়োজন পড়েনা,,,,",0,celebrity
তিনি নাকি কমেন্ট পড়েননা।তাহলে হাসাহাসি করে এটা জানলেন কিভাবে?,0,celebrity
"#জ্ঞানী লোকের জ্ঞানী কথা# স্যার অনেক কিছু না বলে, অনেক কথা বুঝিয়ে দিলেন। ধন্যবাদ।।।।",0,celebrity
"এ ও কি সম্ভব :O মৃত ব্যাক্তির আগমন কিভাবে ঘটলো? o.O  ভূভূভূভূ্ভূত ভূভূভূভূভূত আমার কমেন্ট করতে হাত,পা কাপছে ভয়ে :'(",0,celebrity
একরাশ বমির মধ্যে সাঁতার কাটিতেছেন আপনি স্যার😂😝,0,celebrity
কমেন্ট পড়ে মজা নিবার আইসি ।,0,celebrity
"জামায়াতের বিরোধিতা করা কোনো সমস্যা না।এটা তো বাংলাদেশের 'ফ্যাশন' এর মধ্যে পড়ে।তাছাড়া জামায়াতের বিরুদ্ধে বললে/লিখলে অনেক গুনা(কৃত অপকর্ম) ও মাফ(বিশেষ শ্রেণীর কাছে) হয়। কিন্ত জামায়াতের বিরোধিতা করার জন্য দেশের কোটি কোটি মানুষের মানবাধিকার, মৌলিক অধিকার পর্যন্ত দলনকারী একটি স্বেচ্ছাচারী রাষ্ট্রীয় কর্তৃপক্ষকে সমর্থন করা,তাদের তাবেদারী করাতো অারো জঘন্য মানবতাবিরোধী অপরাধ।",0,celebrity
"আমি খুব ভয়ে ছিলাম! আপনি বেঁচে আছেন তো স্যার! এই বাংলাদেশে আপনার মতো জ্ঞানী গুনীদের নিয়ে অনেক ভয় হয়! না জানি কি হয়ে যায়! সাবধানে থাকবেন! বের হবেন না বাইরে! বাইরের অবস্থা খুব খারাপ! আন্দোলন চলতাছে""!",0,celebrity
নকলবাজ,0,celebrity
"বিদেশী  মদের সাথে আর দেশী কমেন্টস গুলা পড়া সেই লেভেলের মজা। হেতেরে আইক্কালা বাশই চাই। না পারবে কইতে,না পারবে সইতে। কেমন বোধ করছেন ষার জাফর ইকবাল??",0,celebrity
"আমার ভাইএর রক্ত লাল, জাফর কোন *********ল",0,celebrity
"বিশ্ববিদ্যালয় শিক্ষকদের কি রাজনৈতিক অবস্থান থাকতে নেই? দলীয় রাজনীতির প্রতি সমর্থন থাকতে নেই? প্রশ্ন দুটির উত্তর বেশীরভাগই হ্যা বাচক ভাবে দেবেন তাতে সন্দেহ নেই।কিন্তু বাস্তবতা হলো নব্বুই পরবর্তী সময়ে  শিক্ষক নিয়োগ, পদোন্নতি ও প্রশাসনিক পদায়নের ক্ষেত্রে ব্যাপকভাবে দলীয় প্রভাব এবং ক্ষেত্রবিশেষে দুর্নীতি অবস্থা নাজুক করে তুলেছে। অনেক বছর ধরেই অনেক যোগ্য ব্যাক্তিদের বাদ দিয়ে দলান্ধদের ভিসি হিসেবে নিয়োগ দেয়া হয়েছে। এর ফলে পাব্লিক বিশ্ববিদ্যালয়গুলো উপযুক্ত মানুষের সেবা থেকে বঞ্চিত হয়েছে। ভিসিদের চরিত্রের সাথে ডিসিদের মিল বেশী।অর্থাৎ দুই আনা শিক্ষাবিদ হলে চৌদ্দ আনা প্রশাসক। পাব্লিক বিশ্ববিদ্যালয়ের ভিসি নিয়োগে আমরা কোন  ঐতিহ্য বিনির্মাণ করতে পারিনি বরং ছিটেফোঁটা যা ঐতিহ্য ছিল তাও ধ্বংস করেছি।  শিক্ষক হিসেবে আপনি কেমন প্রভাব ছাত্রদের জীবনে রাখতে পেরেছেন তা আপনার ছাত্ররা ভাল বলতে পারবেন।তারাই বলতে পারবেন আপনি কতখানি দায়িত্বশীল ছিলেন, পক্ষপাতদুষ্টতা ছিল কিনা, বিশেষ সংস্কার আপনার দায়িত্বে প্রভাব ফেলেছিল কি না।তবে এক জন শিক্ষক ব্যক্তিত্ব হিসেবে আপনার ছাত্রছাত্রীর বাইরেও তরুণ সমাজে আপনার প্রভাব ব্যাপক তাতে সন্দেহ নেই।এটি একটি বিরাট সুযোগ যা এখনো  একই রকম ভাবে কাজে লাগতে পারে। আপনি অসাধারণ মেধাবী এবং আমাদের সমস্যা আর সম্ভাবনা খুব ভাল বুঝেন।  এই অপার সম্ভাবনার জায়গা থেকে নির্মোহ কাজ করার সুযোগ আপনার সব সময়ই থাকবে। আগামীর জন্য আপনার প্রতি শুভেচ্ছা।",0,celebrity
কমেন্ট পড়ার জন্য আসছিলাম,0,celebrity
আপনি কি অভিজিত এর ব্লগ পরে দেখসেন?? উনি কি অসভভ ভাসায় ইসলাম কে কতাক্ষ করেসে আপনি কি জানেন??? মুক্তমনা নাকি অন্য ধর্ম অবমাননাকারি???,0,celebrity
"আপনারা বুদ্ধিজীবি। ছোটখাটো আন্দোলনে তো ঠিকই লাফাইতে লাফাইতে চইলা আসেন। এখন তো বড় আন্দোলন হচ্ছে। কি এমন সমস্যা যে লেজটা গুটায়ে ফেলসেন? কিছু বলেন না বলেন,এটলিস্ট স্টুডেন্টদের কাছে আসেন,সাথে দাড়ান। কথা বলেন। না তা না। একটা পোষ্ট দেই,তারপর রামনাম! সুশীল না হয়া জনগণের অংশ হন। ঠিক জায়গায় থাইকা লাথি খাওয়াও জায়েজ।",0,celebrity
"ধর্ষকরা আপনার আপনলোক। তাদের মাথায় একটু হাত বুলিয়ে আপনি বুঝিয়ে বললেই হবে!   এখন তো বর্ষাকাল না, তাই নিজের লোকেদের ওপর অভিমান করে আবার শীতের রাতে বাইরে বসে থাইকেন না, ভোররাতে কেউ ভুলে তাহাজ্জুদের দাওয়াত দিয়া বসলে তো জঙ্গি বলে ধরায় দিবেন আবার!   🙉🙉",0,celebrity
"ভালবাসি আপনাকে,,,,,,   আপনার পাশে গনজাগরণ মঞ্চে অনেক বসেছি কিন্তু আপনাকে তখন চিনতাম না,,",0,celebrity
এখানে এত বেশি বিনুদুন যে আগামীতে comment পড়তে মনে হয় ডলার লাগবে৷,0,celebrity
"ওনি আসলে জানেন না কিন্তু টূট মারতে পারেন,,, সিস্টেম ওপেন আছে লাগলে বইলেন,,,,",0,celebrity
"হইছে তুমরা বাদ দেও,উনার গায়েবানা জানাজা পড়তে হবে না,উনি বাইচ্ছা আছেন।",0,celebrity
আমরা ছাত্ররা এখন কী করতে পারি?,0,celebrity
আপনাকে কি লিখালিখি করার জন্য সরকারের পারমিশন নিতে হয়? শেষ মুহূর্তে ক্রেডিট নিতে আসছেন! বেঁচে আছেন শুনে ভালো লাগলো।,0,celebrity
কে বলছে উনি আন্দোলন সমর্থন করেননি?😲😲  উনি তো এই কয়দিন হাইকোর্টে নিরাপদ সড়ক সমর্থন রায়ের জন্য উফুড় হয়ে শুয়ে ছিলেন😂😂😂   মানোস😜,0,celebrity
দেরি করে ফেললাম !,0,celebrity
"এতদিন সবাই আপনার বিরুদ্ধে কথা বললেও কখনো একটা খারাপ কথা আপনাকে নিয়ে বলিনি . .সর্বদা সাপোর্ট করে এসেছি..কেউ আপনাকে নিয়ে খারাপ কিছু বললে তার প্রতিবাদ করেছি কিন্তু আজকে আপনি আপনার ছাত্রসমাজ,আপনার ভক্তদের অনেকটা ছোট করে দিলেন এই পোস্টের মাধ্যমে😞 অধিকারের জন্য লড়াই করলে কি রাজাকার আখ্যা পেতে হয় স্যার? আপনার এই পোস্ট করার কারণ টা বুঝলাম না ...বুঝতে পারলাম না কেন ছাত্রসমাজকে ""রাজাকার"" বলে আখ্যায়িত করলেন!😞",0,celebrity
উদ্ভোটনিয়াম+ দালালীয়াম+ অভিনোনীয়াম+ লেখাচুরিয়াম= জ্রাফ্রোনিয়াম,0,celebrity
জাফর স্যারের কমেন্ট বক্স বিনোদনের জগত,0,celebrity
"কিসের জন্য যে এই বেচারা পোস্ট দেয়,  না, সরি! পোস্ট না দিলে আমাদের মতন মানুষরা বিনোদন পাবো কোথা থেকে।লাগে রাহো মুন্না ভাই........",0,celebrity
এ কে খন্দকার বইটি লেখননি প্রথমা প্রকশনী তাকে দিয়ে বইটি প্রস্তুত করিয়ে ছিলেন৷ আমরা প্রথমা প্রকাশনীর এই দুশ্কর্মের দৃষ্টান্তমূলক শাস্তি দাবি করছি,0,celebrity
কমেন্ট পড়তে চিলে আসলাম😃😃😃,0,celebrity
"নির্বাচনী ইশতেহারে কী থাকবে সেইটা লিখতে আসছেন?আর সেই নির্বাচনে আমি/আমরা আমাদের মূল্যবান ভোটটি প্রদান করতে পারবো কি-না সেই সংশয়ে আছি।আগে ভোটাধিকার কীভাবে অর্জিত হবে আর রক্ষা করা যাবে সেই বিষয়ে একটা জ্ঞানগর্ভ পরামর্শ দিয়ে জাতিকে উদ্ধার করুন,জনাব😫",0,celebrity
"আমার প্রশ্ন হল selective problem এর selective solution বের করার চেষ্টার মধ্যে সৃজনশীলতার কি আছে...? যে ধরনের প্রশ্ন করা হয়, তাতে শিক্ষার্থীদের অর্জিত বিদ্যার পরীক্ষা করা হয় না বুদ্ধিমত্তার পরীক্ষা করা হয় তা বুঝা মুশকিল। আর যদি বুদ্ধিমত্তার পরীক্ষা করা হয় তবে শিক্ষার উদ্দেশ্য বিদ্যা অর্জন না বুদ্ধিমত্তা অর্জন?",0,celebrity
"স্যার,খুব ভাল লিখেছেন।বিশেষ কাউকে তুষ্ট করতে কিভাবে লিখতে হয় সেটা জানতে,এ লেখাটি সবারই অবশ্য পাঠ্য।",0,celebrity
"এইভাবে ইঁদুর গুলো গর্ত থেকে উঠে আসতে লাগল, এর আগেও উঠে আসছিল ঠিক একি রকম ভাবে.. আচ্ছা গায়েবেনামা নামাজ টা তাহলে কি আর হবে না..",0,celebrity
রাজাকারের রক্ত রাজাকারের ভক্ত রাজাকারগুলোর শাস্তি হওয়া উচিত,0,celebrity
"স্যার আপনি বলেছেন মুক্তিযুদ্ধের সত্যিকারের চেতনার কথা বিএনপি তার ইসতেহারে উল্লেখ করেছে... যেটি আপনি এই প্রথম শুনলেন... আর প্রশ্ন তুলেছেন মুক্তিযুদ্ধের মিথ্যা চেতনাও আছে না কি? মুক্তিযুদ্ধের যে চেতনার আওয়ামীলীগ ধারণ করে তা কখনই সত্যিকার চেতনা হতে পারে না কারন রাষ্ট্রশক্তি ব্যবহার করে হত্যা, জেল, জুলুম, গুম, একতরফা নির্বাচন, ভয়ভীতি দেখানো, ভুয়া মামলা, পেশিশক্তির ব্যবহার, সংবাদমাধ্যম বন্ধ করা, মানুষের মত প্রকাশের স্বাধীনতা খর্ব করা, ভয়ভীতির মাধ্যমে সংবাদ মাধ্যমের মালিকানা পরিবর্তন, ভয়ভীতির মাধ্যমে স্বীকারোক্তি আদায় ইত্যাদি কখনো মুক্তিযুদ্ধের চেতনা হতেই পারে না... মুক্তিযুদ্ধের প্রধান চেতনা হলো গনতন্ত্র ও স্বাধীনতা... যা আওয়ামীলীগ কোন দিন বিশ্বাস করেনি,.. মিডিয়ার সংখ্যা বেড়েছে কিন্তু সেগুলোর মালিক কারা? আর যে  মুক্তিযোদ্ধার কোন মতামত নিজেদের পক্ষে যাবে না তাদের পাকিস্থানের চর বলার মতো অসম্মান(এমনকি খেতাব প্রাপ্ত মুক্তিযোদ্ধা জিয়াউর রহমান, একে খন্দকার, বঙ্গবীর কাদের সিদ্দিকী, শাজাহান ওমর, কর্নেল অলি কে, যারা মুক্তিযুদ্ধে জীবন বাজী রাখার প্রমান দিয়ে স্বীকৃতি অর্জন করেছে) যে দল করতে পারে সে দল মুক্তিযুদ্ধ কে কতটা সম্মান করে তা বুঝতে আপনার মতো পন্ডিত হতে হয় না..",0,celebrity
"কমেন্টে পড়তে আসলাম।  দেখি দেখি একটু সাইট দেন প্লিগ,,,",0,celebrity
"আমি আসলে ফেসবুক, নেট, ব্লগের সাথে পরিচিত নই  sottoi",0,celebrity
"দু্র্নীতির মাধ্যমে যারা নির্বাচিত হয়ে ক্ষমতা নেয় তাদের কাছে আপনি আশা করছেন দুর্নীতিমুক্ত দেশ!...বছরটা শুরু করলেন কৌতুক দিয়ে!...স্যার,চেতনার ঝাঁপিটা বন্ধ রেখে একটু বিবেকটা জাগান...আপনি নৌকার উপদেষ্টা হোন আপত্তি নেই, কিন্তু এত জঘন্য পক্ষপাতিত্ব করেন আপনি! খুব লজ্জা লাগে স্যার!...পক্ষপাতিত্বেরও একটা সীমা থাকে!",0,celebrity
Wonderful Sir..,0,celebrity
স্যার আপনি আবার ফিরে আসুন,0,celebrity
৩০তারিখ কয়টা দিলেন স্যার....?,0,celebrity
আমাদের দেশের ভবিষ্যত কি হবে স্যার? এ ব্যাপারে আপনার মতামত কী,0,celebrity
"আল্লাহ যদি অজ্ঞ রেখে দেন তবুও খারাপ না,কিন্তু আপনার মত জ্ঞানপাপী যাতে না বানায়।",0,celebrity
আপনার প্রভুভক্তি দেখে হিংসে হয় 😎,0,celebrity
"এই আন্দোলনের কোন সাইড ইফেক্টস নাই পুরোপুরিই ভেষজ,,কিন্তু কোটা আন্দোলনের ছিল অতি মাত্রায় সাইড ইফেক্টস ।তাই তার মাঝেমধ্যেই বমি আসিত;!!!  কারোর কষ্ট হচ্ছে না,রিক্সাওয়ালা,আম্বুলেন্স,স্কুলগামী শিক্ষার্থী,মন্ত্রী সচিব কারোরই নয়।  আন্দোলন দুইটা একই ধরনের,কিন্তু ...... শেষ পৃষ্ঠায় মেলে না,,,তাই বমি আসে।",0,celebrity
অবশেষে তাহার চেতনা জাগ্রত হল😂😂,0,celebrity
"কে তুমি বৎস, ধরিয়া মৎস, বেচিয়া গঞ্জে, অকুল ও কুঞ্জে, না খাইয়া তাজা, কেনো ভক্ষন করিয়াছো মেয়াদ উত্তীর্ণ গাজা 😂",0,celebrity
সব গালি দেওয়া শেষ।বাকি যে কি রইল....,0,celebrity
আপনে তাহলে এখন ও জিবিত আছেন।,0,celebrity
একদিকে সোশ্যাল নেটওয়ার্কের অভিশাপ থেকে মুক্তি চাই বলে অপরদিকে সোশ্যাল মিডিয়াতেই নিজস্ব মতামতটা তুলে ধরলেন!!এর থেকে বুঝা যায় আপনি নিজেও এর থেকে মুক্তনন।আপনি নিজেও এ অভিশাপে অভিশপ্ত😐😐😐,0,celebrity
"Sir, যে প্রজন্ম ইতিমধ্যে অন্ধকারে পতিত হয়েছে তাদের আলোকিত করার চেষ্টায় ব্যস্ত থেকে আমাদের কথা ভুলে যাবেন না।শিক্ষামন্ত্রীর নেয়া সিদ্ধান্ত কতটা যুক্তিযুক্ত বলে আপনি মনে করেন?এ সিদ্ধান্ত আমাদের ওপর অন্যায় ভাবে চাপিয়ে দেয়া হয়েছে বলে আপনি মনে করেন না?স্যার আমাদের ভবিষ্যত্‍ আলোকিত করার জন্য তো অনেক কিছু করলেন এখন আর একটু না হয় করলেন।Pls sir help us,safe us.",0,celebrity
"পেটের ব্যাথায় খুব কষ্ট পাচ্ছিলাম হটাৎ পোষ্ট টা দেখে হাসি লাগছে,বমি করে দিছি....",0,celebrity
আপনার লেখা পড়ে অবাক হই নাই!!! কারণ এ দেশে শুধু শিক্ষিত অবশ্য নামমাত্র কিছু মানুষের জন্য আমাদের দেশের এই অবস্থা!!  আগে তারা বদলালে বাকিরা ঠিকই বদলাবে!!!,0,celebrity
মুক্তিযোদ্ধা বলতে আধুনিক পাকিস্থান বোঝায়। যাদের লোভ আকাশচুম্বি। আজ যদি সরকার মুক্তযোদ্ধাদের অনারিয়াম অন-অগ্রসর গোষ্ঠীদের মাঝে প্রদান করে দেখবেন সারাদেশে মুক্তযোদ্ধাদের আন্দোলনের জোয়ার বইছে।আমি না মুক্তযোদ্ধা না রাজাকার কিন্তু আমার কোন সম্পদ যেন কোন মুক্তযোদ্ধাদের দেওয়া না হয়। আমি ব্যক্তিগতভাবে না পাকিস্থানী মতাদর্শের না মুক্তযোদ্ধারর মতাদর্শের। আমি এমন একটা দেশ চাই যেখানে এই দুই মতাদর্শের লোক থাকবে না। সাথে আপনাদের মত চামচামি  মা্র্কা প্রগতিশীল।,0,celebrity
"আমরা বড়ই অদ্ভুত জাতি। কেউ বা এসি ঘরে বসে মোবাইলে টাইপিং করে বক্তিতা দেই আর কেউবা রাস্তায় দারিয়ে দেই। আজ পর্জন্ত কেউ কি দেখেছেন বক্তিতা অয়ালাদের আঘাত পেতে, কেউ দেখেন নি আমরা হার্স্কার দর্শক। বরই উদ্ভুত হাস্যকার। যারা বক্তিতা কিংবা লেখা লেখির ধারে কাছে নেই তারাই ০ নামক অংক সং্খ্যা টা নিয়ে বাড়ই চলে যায়",0,celebrity
উনিই আসল রাজাকার  জ্ঞান পাপি রাজাকার,0,celebrity
ইম্রান চরকার আর এই ভদ্রলোকের পোস্ট না দেখেই হাহা দিতে হয়। দিয়ে একটু হাসতে হয়। যতই শীত পড়ুক হাসতে নেই মানা।,0,celebrity
আর কতকাল ছলবে এবার একটু থামুন,0,celebrity
"স্যার, আপনার লেখা দীপু নাম্বার 2 আমার পড়া প্রথম বই। এই বইটি পড়েই আমি আপনার ফ্যান হয়ে যায়। তারপর দেড় বছরে আপনার লেখা 22 টি বই পড়েছি। মাত্র কয়েকদিন আগেই আপনার ID খুঁজে পেয়ে যে কী খুশি হয়েছি আপনাকে বলে বোঝাতে পারব না। কিন্তু এই খুশি মরতেও বেশি সময় লাগল না। যখন দেখলাম আপনার পোষ্টের নিচে বেশ কিছু অসুস্থ মানুষের বেশ কিছু অসুস্থ কমেন্ট। মনে হয়েছিল ID টা না খুঁজে পেলেই ভালো হতো। স্যার, আপনাকে কেউ কিছু বললে খারাপ লাগে। এই খারাপ লাগা থেকে বলছি যাদের জন্য লিখলে লাভ হয় তাদের জন্য লিখুন। কেন যেচে নিজে অপমানিত হচ্ছেন??",0,celebrity
বুড়া পাকনার জ্ঞান শোনার টাইম নাই,0,celebrity
কমেন্টে হরহর করে সবাই বমি করতেছে 😂,0,celebrity
খুব ভয় করে কমেন্ট করতে 😒 যদি সাদিক মোটিভেশন ষ্যারের মতো ডিলেট করে ব্যান করে দেয়। 😒  আপাতত এতটুকু কমেন্ট করেই পিতিবিকে বিদায় জানালাম 😖😒,0,celebrity
"আপনার চোখেচোখ রেখে বলবো আপনি একটা অসৎ লোক, ইতিহাসের শিক্ষিত  বাটপার। এদেশে গণতন্ত্র হত্যার দায় আপ্নারো। ইতিহাস আপনাকে ঘৃণা ভরে মনে রাখবে, হর হর করে বমি করবে আপনার উপর।",0,celebrity
"যে চাকরিতে ছয় মাসের অবোধ শিশুকে সন্দেহ করতে হয়, সেই চাকরি না করলে কী হয়?😕😕স্যার চাকরি তো ছেলের হাতের মুয়া😣চাইলে একটা বাদ দিয়ে আর একটা নেওয়া যায়",0,celebrity
YESS!!!,0,celebrity
ছন্দে ছন্দে ছোটদের জাফর ইকবাল ------------------------------------------------ বাঁচতে চাইলে মর্ত্যে থাকতে হবে গর্তে যেমন করে বাইন মাছেরে কাদায় পায় না ধরতে।  লাগলো দেশে যুদ্ধ হইয়া আমি ক্রুদ্ধ জ্ঞানী হইতে গর্তে লুকাই বই খাতা সব সুদ্ধ।  ঢিসুম যুদ্ধ খুব গর্তে দিয়া ডুব ভীষণ রকম গল্প ফাঁদি কাটতি হবে খুব।   যুদ্ধ দিনের শেষে মোচ উঁচিয়ে হেসে গর্তে পাওয়া গল্প বেচি নিলাজা কাশ কেশে।,0,celebrity
"আপনার এতদিনের নীরবতাই প্রমাণ করে, আপনি দেশের মানুষকে ভালবাসেন না। ভালবাসেন ক্ষমতাসীনদের চামচামী।",0,celebrity
আপনারা যারা কমেন্ট করতেছেন প্লিজ বানানের দিকে খেয়াল রাখবেন যাতে করে আমরা যারা কমেন্ট পড়ে বিনুদুন নিতে  আসছি তাদের কোন প্রকার অসুবিধা না হয়। 😛,0,celebrity
"চশমাটা উনাকে মনোবতার আম্মাজানে গিফ্ট করছে। অন্যকিছু আর চোখে পরে না। মুতিয়া আফার লগে পিরিত লাগছে হয়তো।তাই অফ টপিকে আবার একটু ফেবুর ঘসা দিলো। বিআওয়ামীপন্থী,কটিচাটা দালাল।",0,celebrity
আপনি কে ষ্যাড়😂😂  কবর থেকে আসলেন কবে😱😱,0,celebrity
জ্ঞান হারান নাই আবার জ্ঞান হারাইছেন  চেতনা অচেতনার মাঝে আছেন  তাও কত কিছু মনে আছে আর কত কিছু লিখে ফেললেন  ওরে সাবাস 😂😂😂,0,celebrity
"|| সুখবর! সুখবর!! সুখবর!!! ||[] ""রবির আকর্ষনীয় 3GB ইন্টারনেটঅফার"" [][]""পোষ্টটি শেয়ার করুন এবং আপনারবন্ধুদের জানান,বোনাসইন্ট ারনেট,ফ্রি ইন্টারনেট প্রিয়বন্ধুরা-রব ি সীমদিচ্ছে বাম্পার বোনাসইন্টারনেট। মাত্র 30 টাকায়3GBইন্টারন েট মেয়াদ 60 দিন ।[] অল্প টাকায় যারা সব সময় বোনাসইন্টারনেট অফারেরঅপেক্ষায় থাকেনতারা ধন্যবাদ দিনরবি'র এইধামাক্কা অফারে।[] ইন্টারনেটহ্যাকহ ওয়াটা একটি স্বাভাবিকপ্রক্র িয়া। শুধুতাই নয়সথে থাকছে,100মিনিট টকটাইম,300SMS& 300 MMS। []নিয়মটা বলছি মনদিয়ে দেখুন,""আসলে খুঁশিতেনাচ...বে ন""।30 টাকায় 3GB ইন্টারনেটআনতে আপনাকে যা করতে হবে- (¡)মোবাইলে 35টাকা, বা তারবেশি রাখবেন।(¡¡)তারপ র রেজিশ্ট্রেশন করুন রবি'রআকর্ষনীয় ধামাক্কা অফারে।রেজিশ্ট্র েশন করতে Message এ যান-গিয়ে লিখুন 30 তারপর Send করুন 121201832323755 এই কোড নাম্বারে।(¡¡¡)র েজিশ্ট্রেশনহয়ে গেলে একটা Confirm Messageআসবে,এবা র ডায়াল করুন*8474*2*1#, আপনার কাজ শেষ![]কয়েক সেকেন্ড অপেক্ষা করুন। তিনটি Message আসবে এবার 3GBদেখতে ডায়াল করুন*8444*88#, মিনিটদেখতে *8444*28#,SMSদে খতে *222*2# &MMS দেখতে *222*1#।[]শেয়ার করলে সবার উপকার হবে। (বিঃদ্রঃ যারা পেয়েছেনতারা Likeদিয়ে যাবেন,আর যারা আনতে চান তারা চেষ্টা করুন,অফারটা ১৬ ডিসেম্বরের ২৫ তারিখ পর্যন্ত আছে। অসুবিধা হলে জানান।",0,celebrity
আচ্ছা আমাদের এই মহান মুক্তিযুদ্ধের চেতনার ফেরিওয়ালা নাকি যুদ্ধের সময় টগবগে যুবক হওয়া সত্ত্বেও পালিয়ে বেড়িয়েছেন।কথাটা কি সত্যি নাকি গুজব!? আমি আবার গুজবে কান দেইনা!,0,celebrity
আপনাদের মতো মেধাবির জন্ম হউক বাংলার ঘরে ঘরে,0,celebrity
২০১১:আমার বন্ধু রাশেদ ২০১৮:আমার বন্ধু রাশেদ না(কোটা আন্দোলনকারী ছাত্র) হড় হড় হড়ড়,0,celebrity
কমেন্ট পড়তে আসছি! :3,0,celebrity
কমেন্ট পড় লাইফে সবচেয়ে বড় বিনোদন পাবি। Niti Sultana,0,celebrity
"হাবিবের গান মনে পড়ে গেলো,""এতদিন কোথায় ছিলে!!"" 😂😂",0,celebrity
"সার, আপনি তো সুন্দর করে মুক্তিযুদ্বের কথা স্বরন করিয়ে দিলেন।কিন্তু বর্তমানে যারা মুক্তিযুদ্বের নাম বিক্রি খাচ্ছে তাদের বিষয়ে পরিস্কার করে কিছুই  বললেন না?",0,celebrity
আমাদের এই দেশ গুনিদের মূল্য দিতে জানে না।।।।আর তার জন্যই এই অবস্তা।,0,celebrity
শ্রী শ্রী হড়হড়ানন্দ বমিকবাল ধ্রোনাচার্য!,0,celebrity
আল্লাহ আপনি বাঁচি আছেন? বিশ্বাস করেন ভাবছিলাম মরে গেছেন।,0,celebrity
স্টুডেন্টদের মৃত্যুতে কোনো শোক নেই😭😭😭  আসল শোক তো হবে ১৫-ই আগস্ট😢😢😢,0,celebrity
স্যার পটোল ক্ষেত থেকে কিভাবে ফিরে এলেন?,0,celebrity
"স্যার.... আমি আপনার লেখা দেখলে মন দিয়ে পড়ি। আমি সবসময় একটা কথা জেনে আসছি আপনি রাজনীতি জানেন না, বুঝেন না। আপনার বিভিন্ন লেখা থেকেও সেটা জেনেছি অনেকবার। কিন্তু নির্বাচনের আগে হঠাৎ করে এমন রাজনৈতিক বিশেষজ্ঞ হয়ে গেলেন স্যার!! লিখলেন তো ভালই....তাই বলে এমন পক্ষপাতমূলক, একচোখা!!  লোকজন যে 'দ' আদ্যক্ষর দিয়ে আপনাকে গালিগালাজ করছে স্যার....☺☺",0,celebrity
জোকার,0,celebrity
কমেন্ট পড়তে আসলাম😊,0,celebrity
কারো শারীরিক বা মানসিক যন্ত্রণা থাকলে কমেন্টসগুলা পড়তে পারেন। 😁😁😁,0,celebrity
আমি অবধারিতভাবে হরহর করে বুমি করে দিব।,0,celebrity
"ইতিহাসের ইতিহাস নিয়ে কিছু কথাঃ ১ শ্রদ্ধেয় জাফর ইকবাল স্যারের কোনো লেখার সাথে আমি কখনো দ্বিমত করি নাই। স্যারের আজকের লেখা পড়ে মনে হলো মুক্তিযোদ্ধা হলেই সাত খুন মাফ। তাহলে তো জেড ফোর্সের প্রধান মেজর জিয়া, বীর উত্তম খেতাব পাওয়া মেজর জিয়া আর পরবর্তিতে হাজার হাজার বাংলাদেশ প্রতিরক্ষা বাহিনির মুক্তিযোদ্ধা অফিসারদের হত্যা করা জেনারেল জিয়া, কর্নেল তাহেরকে হত্যা করা জেনারেল জিয়া, মুক্তিযুদ্ধ যার হাত ধরে এসেছে সেই বঙ্গবন্ধুকে হত্যার ষড়যন্ত্র জানা সত্বেও মৌন সমর্থন দেয়া জেনারেল জিয়াকে একজন মুক্তিযোদ্ধা হিসেবে সাত খুন মাফের সুত্রে ফেলে শ্রদ্ধা করা উচিত!   স্যার, ক্ষমা করবেন আপনার এই ভক্তটাকে। পারলাম না আপনার কথা রাখতে। আমি বিশ্বাস করি একজন মুক্তিযোদ্ধা পরবর্তি জীবনে ভুল করতে পারেন, আর সেটার জন্য তার সমালচনা করার অধিকার সবাই রাখি। আইনত দন্ডনীয় কাজও করতে পারেন, সেরকম করলে আদালতে তার বিচার দাবীও করতে পারি। সাদাসিদা কথার আড়ালে স্যার অন্যায়কারীর পাশে দাড়াবেন না প্লিজ।   স্যার আপনি বিশাল মানুষ, আমরা সাদাসিধে। আমরা বীরত্ব দেখলে যেমন গলায় ফুলের মালা দেই, পা ছুয়ে সালাম করি তেমনি তার অন্যায় দেখলে সেটার জন্য সমালোচনাও করি, প্রতিবাদ করি, প্রতিরোধ করার চেষ্টাও করি।   একজন রাজাকার সবসময়েই রাজাকার, কিন্তু একজন মুক্তিযোদ্ধা সবসময় সেটাই থাকবেন বলা চলে না।  [পুনশ্চঃ দুঃখিত স্যার, বঙ্গবন্ধুকে হত্যাকারী মুক্তিযোদ্ধা ডালিম, রশিদ এদেরও সম্মান দিতে পারছিনা। ]",0,celebrity
"কমেন্স পড়ে হাসতে হাসতে পেট ব্যথা করছে,  ওফ্ বমিই এসে যায় নাকি?",0,celebrity
"যিনি আপনাকে আমাকে সৃষ্টি করেছেন তিনি মহান ও ক্ষমাশীল। এখন উচিত হবে আল্লাহর শুকরিয়া গ্যাপন  করা এবং তারই প্রশংসা করা, যিনি আপনাকে সুস্থতা দান করেছেন।",0,celebrity
এইসব শিশু শ্রেনির কিন্ডারগার্টেনে বললে শিক্ষার্থীরা উপকৃত হতো।,0,celebrity
স্যার আপনার মত বেহায়া মানুষ আমি দেখিনি।,0,celebrity
আমরা যে আপনার গায়েবানা জানাজা পড়ে আসলাম। সেটার কি হবে!😑,0,celebrity
আপনার মতো সুবিধাবাদী  লোকদের জন্য একগাদা ঘৃনা,0,celebrity
"কমেন্ট পড়তে আসছি। মন ভালো না,তাই একটু হাসি দরকার।",0,celebrity
"কোনো মেডিকেল এমার্জেন্সি ছিল, আর ছাত্ররা এম্বুলেন্স আটকে রাখছে এমন কথা কেউ পারলে বলুক।আঙুল ফুলে কলাগাছ হলে যে জনসাধারণকে চোখে পরে না তার আদর্শ উদাহরণ হলেন (বুইঝা নিয়েন)।",0,celebrity
"""""চেতনার ফেরিওয়ালা"""" কোথাকার অাপনার  তো জানাজা হয়ে গেছে অাবার এখানে কেমনে এলেন,,,,??",0,celebrity
"আসল কথা হচ্ছে স্যার,,,,,,, আপনি সত্যিই,,,,,মাহান পুরুষ,জাতীর গর্ব,,,.  তাইতো ভালবাসি আপনাকে।",0,celebrity
"১__নারীশিক্ষার নাম করে যদি নারীনির্যাতনের ফন্দি করেন তাহলে তো দেশ গোল্লায় গেলোই! নারীকে যে পুরুষের সাথে বসিয়েই শিক্ষাদান করতে হবে___এমন চিন্তা তো উন্মাদ না হলে করা যায় না। নারীর জন্যে স্বত্রন্ত্য শিক্ষালয়ই চিরকাম্য।  ২__আল্লামা আহমদ সফি হুজুর হাফিযাহুল্লাহর বক্তব্য অসম্মানসূচক ও বৈষম্যমূলক মনে হয় আপনার কাছে??বাহ,,,আপনার তো মনে হবেই____বোকা বিজ্ঞানী........!!!আল্লামা আহমদ সফি সাহেবের বক্তব্য শতভাগ যৌক্তিক এবং প্রকৃত নারীঅধিকারের বাস্তবায়নপ্রত্যাশী!! বেগানা শিক্ষক/সহপাঠীকে নারী-ধর্ষণ করার রাস্তা করে দেয়ার উদ্দেশ্যমূলক কুপ্রচার/কর্মকান্ডকে শক্ত হাতে দমন করতে বাংলাদেশী জনতা সচ্চার জাগ্রত। আপনাদের মতো সমাজবিচ্ছিন্ন বেআকল লেখকদেরকে দু'টাকা দিয়ে গণতেও বাংলাদেশ রাজি নয়!!!  ৩.সন্তানের জন্মদান কি গুরুত্বপূর্ণ নয়?? চাকরানী করা/রাস্তায় ডিউটি করা/পরিবার থেকে দূরে সময় কাটানোটাই গুরুত্বপূর্ণ?? আরে ছাগল______নারীর মাতৃত্বকে হেয় করে কোন নারীসোহাগ দেখাচ্ছেন জাফর মিয়া?!! বাংলাদেশ কিন্তু বেশ্যাক্যান্ট্রি নয় ; বাংলাদেশের মেয়েরা জারজ সন্তানের কলঙ্ক নেয় না। তারা নীতিবান ধার্মিক সন্তানের জননী হওয়ায় গর্ববোধ করে।  ৪__আর আপনারা,,,,,জাফর-টাইপ যারা ; বাংলাদেশ তাদের জন্যে নিরাপদ না। কোন  মুসলিম রাষ্ট্রই না। আপনারা কোন জেনালিপ্ত বেশ্যা মুশরিক ক্যান্ট্রিতে আবাস গড়ার চিন্তা-ভাবনা করেন। ব্যস,,,,,,,,,,,এটুকুই!! আপনার কল্যাণকামী___সো ভালো হয়ে যান।।",0,celebrity
একটা সম্মানিত মানুষ কতো দ্রুত অসম্মানিত জনে পরিনত হয় আপনি তার প্রকৃষ্ট উদাহরণ।কমেন্টস পড়ে আজ আর ঘুম হবেনা।,0,celebrity
"""কিন্তু""",0,celebrity
"""শেখ হাসিনার উপর আস্থা রেখে দেশের মানুষ তাঁর দলকে বিশাল একটি বিজয় উপহার দিয়েছে""-এই জোক্সটি বলার মাধ্যমে আপনি বর্তমান সরকারকে অপমান করেছেন!😂",0,celebrity
প্রচুর মারতে হবে! আইমান ছাড়িকের কাছ থেকে দশ মিনিট লোন নিয়ে মেয়াদোত্তীর্ণ গাঁজা খাইয়ে এই গর্তজীবী চেতনা যোব্ধাকে গদাম মারতে হবে!,0,celebrity
"ভালো থাকবেন স্যার! আপনার হাতের স্পর্শ বোধ-হয় আর পাওয়া হবেনা। চেয়েছিলাম সাস্টে পড়বো, আপনার ডিপার্টমেন্টের ছাত্র হয়ে।  কিন্তু সেটা বোধ-হয় আর পূরণ হবেনা।  যাইহোক স্যার- ভালো থাকবেন। অন্তরের শুদ্ধতম স্থানে আপনাকে যেই জায়গায়া টা দিয়েছি সেখানটা আর কেউ কোনোদিন দখল করতে পারবেনা।  নেভার এভার <3",0,celebrity
সেদিন কি বৃহস্পতিবার ছিল?,0,celebrity
"এত বড় বড় কথা এখন কইতেসেন স্যার, এই সব ক্রিমনালদের অতীত কাজ গুলোকে আপনার মত শিক্ষিত কুলাঙ্গাররাই জাস্টিফাই করে  গন ধর্ষনের পথ তৈরি করেছেন আপনারা। এখন গরু মেরে জুতাদান করতে আসছন। এই মহিলা যদি প্রকাশ্যে তার পছন্দমত প্রার্থীকে ভোট না দিয়ে গোপনে ভোট দিতে পারতো তাহলে আজ তাকে রাজনৈতিক প্রতিহিংসার শিকার হওয়া লাগতো না। এই মহিলাকে নিজের জীবনের ও সম্ভ্রমের ঝুকি নিয়ে কেন প্রকাশ্যে ভোট দিতে হল সেই প্রশ্ন আগে নিজে কে করেন।",0,celebrity
"পাকা আম কাঠালের রসালো মাস ,থাক না স‍্যার এর পাকামো কথা গুলো একটু না হয় শুনি।বুদ্ধিজীবী বলে কথা।",0,celebrity
ঘুমালে হিসাব থাকেনা,0,celebrity
"আমি সেই রাজনীতি চোখ দিয়ে দেখব; কিন্তু মন থেকে বিশ্বাস করতে হবে কে বলেছে?""",0,celebrity
কিছু বলার নাই।উত্তর কোরিয়ায় যে বাস করি।,0,celebrity
পড়িনাই 😖,0,celebrity
"অনেক লম্বা পোষ্ট তো! তাই লিখতে তিনদিন সময় লাগসে! তাছাড়া স্যার মনেহয় বাংলালিংক ইউজার। টুজি নেট স্পিডে লেখাটা পোষ্ট হতে আরো বেশি সময় লেগে গেসে!  দুনিয়া গোল্লায় যাক, উই লাভ ইউ স্যার! গর্ত থেকে বের হয়ে অনেক বালও পোষ্ট লিখেছেন। এভাবেই আমাদের পাশে থাকবেন প্লিজ 😊💘",0,celebrity
"কিরে মেরুদণ্ডহীন বুদ্ধিজীবি,তুই যে বর্তমান সরকারের দালাল সেইটা বুঝি দেশবাসী জানে না!😕",0,celebrity
আপনার সাথে সরাসরি দেখা হলে আপনার সাথে একটা সেলফি তুলব..  :p :p,0,celebrity
"শেখ হাসিনার ওপর আস্থা রেখে দেশের মানুষ তাঁর দলকে বিশাল একটি বিজয় উপহার দিয়েছে।   এই লাইন পড়ে যদি আপনার হাসি না পায়, তাহলে আপনি ডাক্তারের শরনাপন্ন হউন 😳 আপনার চিকিৎসা দরকার 🐸",0,celebrity
ইসলামের পবিত্র সংস্কৃতির সাথে তাহলে হিন্দু আর খ্রিস্টীয় সংস্কৃতির সংমিশ্রণ করেছেন আপনারা,0,celebrity
যাক স্যার অন্তত এটা জেনেছেন যে ওনাকে সবাই গালি দেয় । 😁😁,0,celebrity
ঝহজ্ঝ,0,celebrity
জনাব কোটাবিরোধী আর কোটা সংস্কারন্থী এর অর্থ বোঝেন? আমরা কখনোই কোটা বিরোধী ছিলাম না ছিলাম কোটা সংস্কারপন্থী! যাইহোক সাহিত্য লেখার আগে শব্দ চয়নের দিকে সতর্ক হবেন!,0,celebrity
"কি বলবো বুঝতে পারছিনা, সুস্থ হন ভালো থাকেন, জাতীকে আরও অনেক দেওয়ার আছে আপনার, যা দিয়েছেন শোধ তো দুরে থাক, কৃতজ্ঞতা ও জানাতে পারি না, যদি পারতাম তাহলে আজ আপনাকে হাসপাতালে থাকতে হতো না।",0,celebrity
এই লেখাটা পড়তে গিয়ে পেটের ভিতর মোচড় দিয়ে বমি আসছিল।স্যারের আমি একজন বিরাট ভক্ত ছিলাম কয়েকদিন আগেই।কিন্তু কয়েকদিন তিনি সাধারণ ছাত্রদের আন্দোলনের বিরুদ্ধে কথা বলার পর বুঝলাম উনি একজন স্বার্থপর ব্যাক্তি।,0,celebrity
"1970 এর নির্বাচন ছিল স্বাধীনতার পক্ষে ও বিপক্ষের লড়াই৷সেই ভোটে 169 আসনের মধ্যে 167 আসন পেয়েছিল স্বাধীনতার পক্ষশক্তি৷কিন্তু ভোট পেয়েছিল 75%৷প্রায় 25% ভোটার তখন স্বাধীনতার বিপক্ষে ভোট দিয়েছিল,যাদের আমরা পাকিসেবক/রাজাকার হিসাবে চিনি৷সেই রাজাকারদের বংশধররা ডা: জাফর ইকবাল স্যারকে গালাগাল করেছে এবং করছে৷",0,celebrity
পোস্ট না পড়েই কমেন্ট পড়তে আসছি...🙄🙄,0,celebrity
"Rashed Babu'' & ''Shahriar'' কে বলছি......আপনাদের বাপ-দাদারা অনেক চেস্টা করছিল বাংলা ভাষা ঠেকাতে, পারে নাই......আপনারাও পারবেন না......আর আপনাদের লজ্জা করে না বাংলা ভাষায় কথা বলতে ???",0,celebrity
#বিদায়_পিতীবি🤔 #বিদায় 🤓🤓,0,celebrity
আগে পরীক্ষা দেয়াটা ছিল উৎসবের মতো .... রেজাল্ট হলে সবাই আগ্রহ নিয়ে জান্তে চাইত ..আর এখন আমরা আমাদের রেজাল্ট আগে থেকেই জানি!!!  কারণ পরীক্ষা শুরুর আগেই আমাদের  হাতে প্রশ্ন চলে আসে!!!!!!! ... এই লজ্জা কোথায় রাখি!!!!  শিক্ষা মন্ত্রণালয়ের কিছু অসাধু লোকের জন্য কেন সাধারণ শিক্ষার্থীদের এর ফল ভোগ করতে হবে????  শিক্ষার মেরুদণ্ড যারা আজ ভেংগে দিতে চাইছেন সরকার এর উচিত অবিলম্বে তাদের বিরুদ্ধে বেবস্থা গ্রহণ করা .... sir আপ্নার সহযোগিতা কামনা করি .....,0,celebrity
দেখা যাবে ইনিও আয়মান ভায়ার মতো রাস্তায় নেমে আন্দোলনরত শিক্ষার্থীদের জন্য ম্যাথ অলিম্পিয়াডের আয়োজন করছেন,0,celebrity
মুক্তিযুদ্ধের সময় পালিয়ে বেড়িয়েছেন----হাটে হাড়ি ভাঙলেন জাফর ইকবাল!,0,celebrity
"""খোলা আকাশে একটা ভরা চাঁদ। কী অপূর্ব একটি দৃশ্য!  আমি সেই চাঁদটির দিকে বুভুক্ষের মতো তাকিয়ে রইলাম!  পৃথিবী এতো অবিশ্বাস্য সুন্দর? ""   স্যার আপনি কি জানেন ওই ভরা চাঁদটিও আপনার মুখের দিকে স্নেহভরে তাকিয়েছিল?  আর আমরা তাকিয়েছিলাম গভীর প্রত্যাশা নিয়ে যে, আপনি আবার আমাদের মাঝে ফিরে আসবেন!! আমাদের এতগুলো মানুষের ভরসার মুখটিতো এমন জঘন্য অমানুষের কুৎসিত হাতে হারিয়ে যেতে পারে না।",0,celebrity
"কে তুমি বৎস, ধরিয়া মৎস, বেচিয়া গঞ্জে, অকুল ও কুঞ্জে, না খাইয়া তাজা, কেনো ভক্ষন করিয়াছো মেয়াদ উত্তীর্ণ গাজা 😂😂",0,celebrity
স্যারের ১০নং টা খুবই হাস্যকর!!,0,celebrity
"যাক স্যার অল্পের জন্য বেঁচে গেলেন,আপনার জানাজা আর হচ্ছে না।",0,celebrity
আলহামদুলিল্লাহ❤,0,celebrity
সার আপনি কি চামড়ার ব্যবসা করেন।,0,celebrity
"হ স্যার, আপনি কিছু জানেন না! কিন্তু বাতাবী লেবু কিভাবে বামপার ফলন হয়, সেটা জানেন তো?",0,celebrity
বালময় পিতিবি,0,celebrity
"এই দেশে শিক্ষা ব্যাপস্তা ধ্বংস করার জন্য মন্ত্রীর সাথে সাথে, জাফর ইকবালের মত কথিত চেতনাবাজরা দায়ী।",0,celebrity
পোস্ট যেমন তেমন কমেন্টগুলা গর্জিয়াস।,0,celebrity
"স্যার আপনার নিরবতা কী """"হাতুড়ি মামুন """" কে সমর্থন করে না??",0,celebrity
"তাই নাকি???? নির্বাচন না স্যার সুসঠু হয়াছ্যা?  জনগন নাকি আওয়ামীলীগ কে বিশাল জয় দিয়াছ্যা??? জেনে রাখেন, এই ধর্ষনে দায়ি আপনিও। আমিও।  প্যাট প্যাট করবেন না আর। আইজ্যাক আসিমভ এর সায়েন্স ফিকশন কপি পেস্ট করে লিখে অনেক বাচ্চার কাছে ভাল মানুষ হয়েছিলেন, আমার কাছেও ছিলেন।  বড় হয়ে বুঝলাম আপনে কি চিজ",0,celebrity
"চারদিকে RIP লিখে, আপনার নামে সমবেদনা জানাচ্ছে। আমি তো ভাবছিলাম সত্যি সত্যি আপনি মারা গেছেন। তাহলে স্ট্যাটাস লিখলেন কিভাবে? এই কোমলমতী বাচ্চারা আপনারে নিয়ে ঠিক এভাবে মন্তব্য করতে পারলো?  ছিহ : তারপরেও এই বাচ্চাদের আন্দোলনে আপনি কিভাবে সমর্থন দিচ্ছেন যেখানে আপনার হড়হড় করে বমি আসার কথা।। নাকি দুইদিন পরে আবারো পল্টিবাজি কথা বলবেন, ""ছোট ছোট বাচ্চাদের অশ্রাব্য ভাষায় আমি ব্যাথিত হয়েছি, আমাকে ভীষণ যন্ত্রণা দিয়েছে।এরা দেশের ভবিষ্যত তবে ছোটবেলা থেকেই এদের  কুরুচিপূর্ণ ভাষায় প্রমাণ হয় সোনার বাংলা গড়ার প্রতিভা এদের বিন্দুমাত্র নেই, পাক হানাদার বাহিনীর বর্বরতা কিছুটা লক্ষ করা যায়। আমি মোটেও সন্তুষ্ট নই"" 😂😂",0,celebrity
"এখনো সময় আছে আল্লাহুর পথে ফিরে এসো,,,  আর হে, যে খোদার বিরুদ্ধে সবসময় কথা বলে এসেছেন আজ সেই খোদার কাছে আরো কিছুদিন বাচার প্রার্থনা করছেন। এটাই আল্লাহুর কুদরতি।",0,celebrity
"স্যার আন্নেরে দেখা যায়না কেন?কই থাকেন মিয়া, আন্নের সুন্দর সুন্দর কথা গুলা খুউব ভালা লাগে।",0,celebrity
"#বিশ্বে এই প্রথম Android মোবাইলের মাধ্যমে  প্রতিমাসে ১৫০০০/২০০০০ ইনকাম করতে কিভাবে রেজিষ্টেশন করবেন?  #Note: Refer Of Sponsor ID: (16278380)  #Help WhatsApp No: 01771471624    1. Playstore থেকে  ChampCash Digital India App (12MB) install করুন ।   2. ইন্সটল করে ওপেন করুন ।   3. sign up with champcash এ ক্লিক করুন ।  4. নাম, ইমেইল, পাসওয়ার্ড, জন্ম তারিখ, মোবাইল নং, দেশের নাম, বিভাগের নাম, জেলার নাম পূরণ করুন ।   5. Agree terms & conditions এ ক্লিক করুন । এরপর Proceed দিন ।   6. Refer ID এর জায়গায় 16278380 দিন এবং Verify করুন ও সাথে সাথে $1.00 বাংলাদেশের 82 টাকা!   কাজ শিখতে WhatsApp এ যোগাযোগ করুন  করুন: 01771471624",0,celebrity
"ও‌নি, আ‌গে  আ‌ছিল  ষাড়ঁ। এখন হই‌ছে বলদ।",0,celebrity
এটা পড়লে আপনার ভূলটা ভেঙ্গে যাব আমি মনে করি তাই সময় নিয়ে একটু কষ্ট করে লেখাটা পড়বেন। চাঁদের আচড়ঁ,0,celebrity
"স্যার আমরা আপনাকে ভালবাসি.. সত্যিকারের ভালবাসা..  আমাদের ভালবাসাগুলো আপনার চারপাশে চাদর হয়ে আছে, থাকবে। আপনাকে আগলে রাখবে সকল অশুভ থেকে। হাজার বছর বেঁচে থাকুন আর লিখে যান আমাদের জন্যে। 😍😍😍😍",0,celebrity
তিনিই এক আজব মানুষ..,0,celebrity
"হে বাংলাদেশী, বাংলাদেশের জন্য ক্ষতিকর এবং বিপদজনক রাজনৈতিক পরিবার এবং দল কোনটি ?  ১। কোন পরিবার আর দল ক্ষমতা পেলেই জাতীর মেরুদণ্ড শিক্ষা ক্ষতিগ্রস্ত হয়? ৭২-৭৫ এ হয়েছে, ৯৬-২০০১ হয়েছে, এখন হচ্ছে? জাফর ইকবালের মতে, কোন সরকার দেশের শিক্ষার সবচেয়ে ক্ষতি করেছে? দুর্নীতি দমন কমিশনের চেয়ারম্যানের মতে, কোন সরকারের সময় দেশের শিক্ষা ২০ বছর পিছিয়ে গেছে? কোন বর্বর পরিবার আর দলের সময়ে দেশের পাবলিক বিশ্ববিদ্যালয়ে টাঁকার বিনিময়ে শিক্ষক নিয়োগ শুরু হয়েছে ?  ২। বাংলাদেশের কোন রাজনৈতিক পরিবার এবং দল ব্যাঙ্ক ডাকাত। এনালগ যুগে করেছে, ডিজিটাল যুগেও করছে।  ৩। বাংলাদেশে ভোটধিকার হরণ কারী পরিবার এবং রাজনৈতিক দল কোনটি ? কোন পরিবার এবং দল ৭৫ এ ভোটাধিকার হরণ করেছিল? এখন করেছে ?  ৪। কোটার নামে দেশকে মেধাবীদের সেবা থেকে বঞ্চিত করে দেশের ক্ষতি করছে কোন পরিবার এবং দল ?  ৫। বাংলাদেশে হিন্দু তোষামুদকারী সাম্প্রদায়িক পরিবার এবং দল কোনটি ?  এই পরিবার আর দলটিকে সহযোগিতা করে আপনিও কি দেশের ক্ষতিকারন হবেন? নাকি এই ক্ষতিকর পরিবার এবং দলের হাত থেকে দেশকে মুক্ত করতে চেষ্টা করবেন?",0,celebrity
"তিন.  এখন জাফর ইকবালের উপর হামলা নিয়ে আমার মতামত দিই।  জাফর ইকবালের উপর হামলা অবশ্যই নিন্দনীয়, আমি চাইবো যে যুবক এই কাজ করেছে তার কঠোর শাস্তি হউক। আমি জাফর ইকবালেরও শাস্তি চাইবো, উনার মত কিছু মানুষ নিজেদের স্বার্থের জন্য সমাজে বিশৃঙ্খলা সৃষ্টি করে।  আমরা শান্তিতে বাঁচতে চাই, আমরা চাই না আর কেউ এভাবে চাপাতি বা চাকুর মাধ্যমে আঘাতপ্রাপ্ত হউক।  জাফর ইকবালের কর্মের জন্য যদি আগে তাকে শাস্তি দেয়া হত তাহলে এমন যুবকও তৈরি হতোনা। আমরা চাই না এমন যুবক আগামীতে তৈরি হউক তাই কেউ বিশৃঙ্খলা সৃষ্টি করলেই সাথে সাথে ব্যবস্থা নেয়া হউক।  আর বিশেষ অনুরোধ, এই ঘটনার মূল কারণ কি এটাই নাকি অন্য কোনো মোটিভ আছে তাও সঠিক তদন্তের মাধ্যমে বের করা হউক।  ভালো থাকুন সবাই... ✌  বি.দ্র. এখানে যদি উনি ""ভূতের বাচ্চা কৃষ্ণ, ভূতের বাচ্চা রাম, ভূতের বাচ্চা বৌদ্ধ, অথবা ভূতের বাচ্চা যিশু"" এমন নাম দিতেন তখনো আমি প্রতিবাদ করতাম এবং তার শাস্তি চাইতাম।",0,celebrity
হুজুর কিছু কন..... এইডারে...!! Fazlul Hoque,0,celebrity
নামাজ পড়ে খোদার কাছে দোয়া করেন আরো কয়েকদিন হায়াত পাওয়ার জন্য।,0,celebrity
স্যার আপনার চ্যাপ্টা পিন দিয়া চার্জ দেওয়া লাগবো...  আর বাই দ্যা ওয়ে আপনার গল্পটা পড়ে ভ্লা লাগলো 😂🔫,0,celebrity
স্যার আমরা মানুষ হতে পারি নাই। আপনি আবার আমাদের ফিরে আসুন এই প্রার্থনা রইল।,0,celebrity
স্যারের জন্য এক মিনিট নিরবতা। গর্ত মানবের জয় হোক। সবাই মুনাজাত ধরেন। ঐ শালার পুত আমিন ক।,0,celebrity
একজন রিকশাওয়ালা দুইজন বাসের সব যাত্রীকে জানালা দিয়ে বের করে এক এক করে হাসপাতালে নিয়ে গেলে ঐকিক নিয়মে তার কত সময় লাগবে? এইটা গল্প কইলেন না গুল মারলেন। প্রথমবার হাসপাতালে যাওয়ার পথেই তো অন্য লোকদের ডেকে আনার কথা। নাকি নরসিংদিতে এক রিকশাচালক ব্যতীত আর কোন লোক ছিলো না।,0,celebrity
"স্যার আমরা বর্তমান সময়ের প্রয়োজনীয় রাজাকার,,,,কিন্তু বয়স হবার পরেও আপনি প্রকৃত দেশ প্রেমিক ও সাহসী মুক্তিযোদ্ধা হতে পারেন নাই",0,celebrity
চোর পালালে বুদ্ধি বাড়ে' একজন লেখক আপনি। বাচ্চাদের Idol ছিলেন। সামান্য Follower বাড়ানোর জন্য এত্ত বড় স্ট্যাটাস দিয়ে  সিনেমার কি দরকার? 👎👎👎👎👎👎👎👎👎👎,0,celebrity
আমাকে কঁাধানোর জন্য আপনাকে ধন্যবাদ। মায়েদের জন্য অনেক অনেক ভালবাসা,0,celebrity
"স্যার আপনাকে দেশের তরুণ প্রজন্ম আইডল ভাবত।  আর আপনিও রাজনীতির কাছে বিক্রি হয়ে গেলেন? আমরা সাধারণরা দেশের রাজনীতি অন্যভাবে দেখতে চাই যা উন্নত দেশে প্রচলিত। বর্তমানে আমাদের দেশের কোনো রাজনৈতিক দলই এতোটা উদার হতে পারনি। আপনি তাই জাফর স্যার থাকুন, অন্য কিছু নয়!",0,celebrity
একবার চিন্তা করা শুরু করেছিলাম এই পেজ থেকে কোন পোস্ট দিলে তাতে কোন হাহা রিয়েক্ট পড়বে না। আমি এখনও চিন্তা করে যাচ্ছি।,0,celebrity
আপনি আর কত করে যাবেন ? আমার ভাবতে অবাক লাগে !,0,celebrity
গর্ত যোন্ধা দেখি বের হয়ছে,0,celebrity
"স্যার, হতে পারেন আপনি মহাজ্ঞানী ॥ কিন্তু আপনার নৈতিকতার অভাব ! সময় থাকতে সত্যের পথে ফিরে আসুন...",0,celebrity
আপনার লেখা টা পড়ে অনেক কিছু জান্তে পার লাম। ভালো থাকবেন স্যার,0,celebrity
এইবার বই মেলার আগের বই দুইটা ফালতু। প্রতিবছর যে লিখতেই হবে এমন কোন আইন নাই।,0,celebrity
শুয়ার কখনও কচু ছাড়া অন্য কিছু চক্ষে দেখতে পায় না,0,celebrity
yeah,0,celebrity
হ্লার আকাইম্যা.....!,0,celebrity
বস্তা পচা লেখা  একদম !,0,celebrity
"প্রিয় স্যার আমাদের মাঝে বেচে থাকুন শত বছর,আমাদের আলোকবর্তিকা হয়ে।আপনার সুস্হতা কামনা করছি।",0,celebrity
আপনি বেঁচে থাকবেন ভালোভাবেই,0,celebrity
"হেদায়েত এর মালিক একমাত্র আল্লাহ কেউ কোরআন পরে হেদায়ত পাবে আবার কেউ পথবস্ট হবে , আল্লাহতালা আমাদের সমাজ কে ইসলাম বিরুদি পিতনা বাজ নবি বিরুদ্ধতা কারি অলি আউলিয়া বিরুদ্ধতা কারি দের কে হেদায়ত দান করুন",0,celebrity
আমাদের বর্তমান মহামান্য রাষ্ট্রপতি একজন অসাধারণ মানুষ!,0,celebrity
"গায়েবানা জানাযা শেষ করে, শেষকৃত্য অনুষ্ঠানে বিদায়ী ভাষন... মদ খা আর কমেন্ট পড়!",0,celebrity
স্যার তাহলে কি আবার ওই আগের সময়টা ফিরে আসছে যেটা আপনাদের অস্বস্তির কারণ ছিল।,0,celebrity
স্যার! আপনার কলামের একদম শেষ তিনটা লাইনে এসে আটকে আছি! এই তিনটা লাইন কি সত্যিই আপনি লিখেছেন!? কিভাবে স্যার!? ক্যামনে সম্ভব!? খুব জানতে ইচ্ছে করছে কোন দিকের বাতাশে আপনার কলমে জ্বর(জোর বললাম না) আসলো....!!!,0,celebrity
উনি কিছুই জানেন না :D,0,celebrity
স্যার আপনার লেখা পড়লে নাকি সবার ভুমি আসে। আচ্ছা স্যার ওদের কেন ভুমি আসে তা নিয়ে একটা লেখা আসা করছি।,0,celebrity
স্যার ফেসবুকে আপনার গায়েবী জানাজার ইভেন্ট দেখে ভেবেছিলাম কিছু খানা দানা হবে।  তাইলে কি সেটা ক্যান্সেল? :'(,0,celebrity
নয়টা মাস গর্তে লুকিয়ে থাকার কথা কি সহজে ভোলা যায়??? তাইতো স্যার মুক্তিযুদ্ধের কথা কখনোই মাথা থেকে সরাতে পারেননা। পাকবাহিনীর হাত থেকে নিজেকে যুদ্ধকালীন সময়ে নিজেকে আড়াল করে রাখতে পেরেছিলেন এইটাই তো স্যারের শক্তি।,0,celebrity
"স্যার, এতদিন কোথায় ছিলেন?  রাজপথে  আপনাকে দেখা যায় না কেন?",0,celebrity
"যে যাই বলেন, আমি এই পোস্টে কিছু ইতিবাচক বিষয় দেখছি । স্যার ভালো করেই জানেন, তিনিও আজ সত্যি বললে ছাড় পাবেন না আওয়ামী প্রেতাত্মাদের থেকে ।",0,celebrity
সুস্থ হয়ে ফিরে আসুন জাতির ভবিষ্যৎতে 💜💜,0,celebrity
এই না লিখতে পারাটাও তো একটা প্রতিবাদ ।,0,celebrity
ফেসবুকে দেখলাম হেতি নাকি মইরা গেছে?,0,celebrity
"স্যার, চার বাচ্চার মা'কে একটা খোলা চিঠি লিখে বেঁচে থাকবার সাহস দিন। বাধিত হব",0,celebrity
"পাকিস্তান আমলে পূর্ব পাকিস্তানের ( বর্তমান বাংলাদেশের ) জন্য সরকারি চাকরির ক্ষেত্রে কত শতাংশ কোটা বরাদ্দ ছিল ????  যাদের রক্ত , আব্রু , পঙ্গুত্ব আর সাহসিকতার উপর ভর করে আজকে মেধা কোটা ভোগ করছেন , তাঁদের সম্মানের পরিধি কমিয়ে “আপনি মেধাবী” চাকরি হয়তো পাবেন  সাথে “ তুই রাজাকার উপাধি “  ....",0,celebrity
চাচা আপনি রাজনীতি নিয়ে লিখবেন না প্লিজ,0,celebrity
ষার আপনি ইলেক্ট্রিক্যাল  #চশমা বানান যেটা পড়লে জামায়াত শিবির  সব স্বাধীনতার চেতনায়  ফিরে আসবে 🐸 বিজ্ঞানীদের কাছ থেকে রচনা আশা করি না ষার,0,celebrity
আচ্ছা জাফর স্যার কে বিদ্রূপ করতে পারে এরা কারা? ওরা কি বংগ সন্তান নাকি ওদের জ্বীনে পাকি DNA?,0,celebrity
স্যার আপনি বেঁচে আছেন??????,0,celebrity
আপনার লেখা পড়ে বড় হয়েছি৷ আমাদের ভবিষ্যৎ প্রজন্ম যেনো আপনার নতুন বইয়ের স্বাদ থেকে বঞ্চিত না হয়!,0,celebrity
"আপনাকে সুবিধাবাদী, ভন্ড  বলায় যাদের সাথে তর্ক  করেছি, তাদের কাছে আজ ক্ষমা চেয়ে নিলাম।",0,celebrity
রাস্তা র কুকুরের এর চেয়ে ভালো ফেন আছে  আপনার তা নেই। দালালি বন্ধ করেন।,0,celebrity
উপমহাদেশের প্রখ্যাত তেলবাজ 😂,0,celebrity
আসল মজা এই খানে ভাইয়ারা! Creazy Freack Mohammad Nazim Uddin অরণ্য হাসান,0,celebrity
আপনি একজন বিজ্ঞানী। খোঁচাখুঁচি ছাড়া বিজ্ঞানের কি উৎকর্ষ দেখাতে পেরেছেন ভেবেছেন কখনো?,0,celebrity
বুদ্ধিজীবি হলেই যে তার মাথায় বুদ্ধি থাকবে এমন কোন লজিক নাই। তবে আপনার মাথায় বুদ্ধি আছে এটা আমি সিওর;তা নাহলে কি ৭১ এ গর্তে লুকায়া জীবন বাঁচাতে পারতেন🐸🐸,0,celebrity
কমেন্ট জুড়ে এত মেধাবী? 😱😱😱😱 ওয়াও....... নতুন বাংলা গালি অভিধান বানানো যাবে। ক্রেডিট দেব জাফর ইকবাল স্যার কে। রচনায়:সুপার মেধাবী গণ। সংকলনকারী :স্বয়ং,0,celebrity
"ছাত্ররা অনেক শ্রদ্ধা করতেন স্যারকে! কাল দেখলাম গালি দিচ্ছে, এটা অনেক কষ্টের!",0,celebrity
"লিখতে পারবেন কেমনে!!এখন আর জোশ নাই!!তলে তলে ঠিকই ফুর্তি করেন,চেতনার নাম দিয়ে ফায়দা লোটেন!!!খুব আশা রাখতাম আপনার উপর। সব হারাইছি!!!আর ভাল লাগেনা আমাদেরও।আমরাও বিষন্ন।আপনাদের চোখের সামনে আর দেখতে চাইনা",0,celebrity
"নিউরনে অনুরনন বই, আমার জীবনের প্রথম গনিতের ধাধার বই। গনিত অলিম্পিয়াড একটা ভালবাসার নাম। সবকিছুর জন্য অনেক অনেক ধন্যবাদ স্যার।",0,celebrity
"অসাধারণ লেখা স্যারের, 👏😍👏😍👏😍☕ #ভালবাসা_নিরন্তর💜👍🙌✋",0,celebrity
"শেখ মুজিব শুধু আপনার প্রিয় নন,কিংবা শুধু শেখ হাসিনার বাপ নন,তিনি পুরো বাংগালীর জন্য একজন পথ প্রদর্শক ছিলেন। তার প্রতি ভালবাসা প্রত্যেক টা বাংগালীর মনে আছে।কিন্তু এখানে প্রকাশে অনেকেই অনেকরকম।কিন্তু একটা বাজে ব্যাপার কি জানেন,বর্তমান সমালোচিত সরকারের মত কিছু সমালোচিত মানুষের মুখে যখন মুজিবের নামে তেলানি কথা কোনো বাংগালী শোনে,তখনি সে বিরক্ত হয়ে যায়।তার মানে তারা মুজিবে বিরক্ত না,বিরক্ত আপনাদের,আওয়ামীলিগ সরকারের অতিরিক্ত তেলানিতে।যার জন্য একজন সাধারন বাংলাদেশী তার প্রতি ভালবাসা দেখাতে কোন মাধ্যমে যেতে হবে সেটা নিয়ে দ্বীধায় পরে যায়।।।।। , সে যাই হোক,বাংগালী জাতি মুজিব কে ভালবেসে বংগবন্ধু উপাধি দিয়েছিল,ভালবাসার যোগ্য একজন নেতা ছিলেন।একজন বাংলাদেশী হিসেবে তাকে মন থেকেই ভালবাসি।❤",0,celebrity
"এসব ভাইরাল হয় না, শুধু ভাইরাল হয় অপরাধী  🤐",0,celebrity
"যারা আন্দাজ করে করা বলে তারা কুৎসারটনাকারী, মিথ্যাবাদী এবং চোগলখোর।",0,celebrity
"অাই এম নট ইন্টারেস্ট জামায়াত, বি এম পি, শিবির।  এখন এসব কথা বলতে নাই ভাই! স্যারের এই কথার চুদনে, অামি স্যারের বই গুলো পড়ি। এগুলো ভালো লাগে। দালালী..................... Na",0,celebrity
"আপনার অনেক বই আছে আমার কাছে স্কুল থেকেই পড়ছি। হুমায়ুন আহমেদ এর আছে, অনেক ভালো লেখাও আছে। এখন বলুন বড় ভাইয়ের কাছে বই চাইতে গিয়ে আপনাদের কেন নাস্তিক বলে? কেন নাস্তিক দের পাশে থাকছেন?  আপনার  বাবা কে রাজাকার রা মেরেছে তার জন্য পুরো ইসলাম কে শত্রু হিসাবে দেখছেন, হয়ে যাচ্ছেন নাস্তিক। মরার পর তো আল্লাহ আপনাকে চিনবে না।",0,celebrity
খুব খুব ভালো লাগলো অত্যন্ত মনোযোগ দিয়ে আপনার লেখাটি পড়লাম,0,celebrity
"মানুষ কত ভাল আর আত্মত্যাগী হতে পারে সেটা মুক্তিযুদ্ধের সময় দেখেছেন আবার কত খারাপ হতে পারে সেটাও দেখেছেন। আর মুক্তিযুদ্ধের সময় আপনার ভূমিকা অনুযায়ী  আমরা বুঝতে পারি মানুষ কতটা ভীতু আর স্বার্থপর আর আত্মকেন্দ্রিক হয়!মুক্তিযুদ্ধ চলাকালীন আপনার এই ফিল্টার বা মুক্তিযুদ্ধের চেতনাটা কোথায় ছিল স্যার!আপনার মত মুক্তিযুদ্ধ চলাকালীন সময়ে গর্তবাসীর মুখে মুক্তিযুদ্ধের চেতনা শুনতে অনেক বেশি সস্তা লাগে এখন!মুক্তিযুদ্ধ আমাদের সবথেকে বড় সম্পদ ও অর্জন, তাই দয়া করে আপনাদের স্বার্থের খেলায় মুক্তিযুদ্ধকে ঢাল বানিয়ে মুক্তিযুদ্ধকে আর ছোট করবেন না প্লিজ।",0,celebrity
আমি বুঝি না একজনের লেখা ত আরেকজনে নাও ভাল্লাগটে পারে।না ভাল্লাগলে ওনার কলাম অথবা বই পড়বেন না ওনার পেজ অনুসরন করবেন না।এভাবে কমেন্ট বক্সে অসুস্থ্যকর কমেন্ট করে এরকম পরিবেশ সৃষ্টি করার কোনো মানে নেই।,0,celebrity
আমার কিছুই বলার নেই!!!!!! :-O:-O,0,celebrity
ইশ আজ যদি জাফর ইকবাল স্যার বেঁচে থাকতো তাহলে এই পোষ্ট টা পড়ে কতই না খুশি হতো :'( . ato laik ato koment!!!gafor sar gindabad,0,celebrity
মুক্তিযুদ্ধকালীন সময়ে আপনার অবদান কি ছিলো?,0,celebrity
মন্ত্রী হতে চাও বুঝি বাবু😌,0,celebrity
"কমেন্ট গুলো একটু দেখেশুনে করবেন, তিনি যথেষ্ট সম্মানী ব্যক্তি।",0,celebrity
এগুলা এডিট করা যাই।  😜😜😜😜,0,celebrity
"রাজাকার কেউ হয়নি, সবাইকেই অযৌক্তিকভাবে বানানো হয়েছে। যে আন্দোলনে গিয়েছে তাকেই রাজাকার বানানো হয়েছে। তখনতো আপনার বিশ্রী গোঁফগুলোর নিচ থেকে কিছুই বের হলো না। তখনতো আপনি জিজ্ঞাস করেন নি, কেন লাখ লাখ তরুণদের এত ঘৃণিত শব্দ চয়নে অপমানিত করা হচ্ছে! আপনাদের মত জ্ঞানপাপীরা যখন তাদের পাশে দাড়ায়নি তখনই তারা সেই কলঙ্কমাখা উপাধিটাকে পুজিঁ করেই সামনে এগিয়েছে। #পরিশেষে বলবো, আজকের একুশ শতকের রাজাকারদের অবৈধ জনক আপনাদের মত পালিয়ে বেড়ানো কিছু সুবিধাবাদী মুক্তিযোদ্ধারাই।",0,celebrity
আমিই তো সব! বাস্তবতা হচ্ছে এটা😂✌,0,celebrity
চের আপনি শুধু নিজের জানের কথাই ভাবলেন! !,0,celebrity
কোদাল সৈনিক হাজির😁😁,0,celebrity
অনেক ভালবাসা,0,celebrity
আপনার এ লেখা বন্ধ করার অপচেষ্টা সফল হবে না ।,0,celebrity
"অনেক গুলো  কথা নিরপেক্ষতাকে প্রশ্নবিদ্ধ  করলো, সরি স্যার!",0,celebrity
কমেন্ট পড়তে আসলাম। এখন আর আপনার লিখা চমক প্রদ হয়না। তেল ভালো মারেন অসিকার করার কোন মানে হয়না,0,celebrity
"স্যার,এই ব্যথা বাঙালি কোনোদিন ভুলবেনা",0,celebrity
আমাদের দেশে সবচেয়ে বেশি দুর্নীতিগ্রস্থ শিক্ষা খাত।এরা ছাএদের দিয়ে নির্মম একটা বাণিজ্য করে যাচ্ছে।যার কারণ হলো কোটি কোটি টাকা।কিন্তু এটার জন্য ছাএ-ছাএীদের যে দুর্ভোগ সেটা বিশ্ববিদ্যালয় প্রসাশন জানে তবুও কিছু টাকার জন্য এই সিস্টেমটা বন্ধ করছে না।বিশেষ করে ছাএীদের জন্য এটি খুবই কষ্টকর।থাকা খাওয়া থেকে শুরু করে পদে পদে তাদের বিপদে পড়তে হয়।,0,celebrity
"সোনিয়া, তুমি যদি স্যারের পোস্ট পড়ে এখনও বমি না করো, তাহলে শুনো, আমি রিয়ার সাথে কক্সবাজার বীচে শুধু গোসল করেছিলাম। আর কিছু হয় নি ।বিশ্বাস করো, প্লিজ!",0,celebrity
"স্যার ছাত্ররা যদি আপনার তরিকা অনুসরণ করে সবাই গরতে লুকিয়ে থাকতো তাহলে রাস্তায় জ্যাম থাকত না ঠিক-ই,  কিন্তু দেশ আর স্বাধীন হত না। #আন্দোলন কখনো পালিয়ে বা লুকিয়ে বা ঘরের মধ্যে হয় না। #যে কোন আন্দোলন যদি তা ১০০ ভাগ ন্যায্যও হয়ে থাকে, তার জন্য আন্দোলনকারি এবং কিছু নিরিহ মানুষ ক্ষতিগ্রস্ত হবেই। কিন্তু যারা দেশ-কে ভালবাসে তারা সে কষ্ট সহ্য করে হাসি মুখে ন্যায় প্রতিষ্ঠার জন্য। #আশাকরি স্যার একদিন আপনার ভুল ভেঙে যাবে।",0,celebrity
"আপনাকে মাদা** চোদ বলে গালি দিয়ে ছোট করতে চাইনা,কারণ আপনি সেই জায়গার ও নিচু স্তরের লোক, আপনার দলে যখন জামাত ইসলাম ছিল তখন সেটা জায়েজ ছিল।আর বি-এন-পির সাথে যখন ঐক্য করে তখন সেটা হারাম হয় যায় না!!!",0,celebrity
ভালো লাগলো আপনার মতো লোক শহিদুল আলম কে নিয়ে লেখার জন্য।,0,celebrity
বাইন...,0,celebrity
"আপনি আছেন,আপনি থাকবেন চিরকাল,মাঝখানে ভ্যানিস হয়ে যাবে ঘাতকের দল।",0,celebrity
"যেদিন কোন মেয়ের সাথে সেলফি তোলার মুড থাকে না, সেদিন আসে আর্টিকেল নিয়ে। ভালোই।",0,celebrity
"বাঙ্গালি চান্দে যাওয়া সাঈদিকে মূল্যায়ন করবে।জাফর ইকবাল স্যার এর মর্ম এরা বুঝতে পারবেনা।হ্যা আমি জামি জাফর ইকবাল স্যার সুবিধাবাদী লেখক।তাই বলে তার জ্ঞান,বিজ্ঞানকে ফেলে দিতে পারিনা।তার সুবিধাবাদী চরিত্রের জন্য তার বই পড়বো না এমনটা নয়।",0,celebrity
যে দেশে গুনি জনের কদর হয় না সেই দেশে গুনি জনের জন্ম হয়না।,0,celebrity
আমিই কি একমাত্র ব্যক্তি!! যে প্রতিদিন বিনোদন মূলক পোষ্ট খুঁজে বেড়ায়!!! ধন্যবাদ স্যার আপনার জন্য প্রাণ খুলে হাসতে পারছি।,0,celebrity
স্যার কিছু নরপশু আপনাকে বাজে কমেন্ট করছে / করবে তাতে আপনি মন খারাপ করবেন না আসলে এসব গণ্ডমূর্খ তারা আসলে জানেই না আপনার ব্যস্ততা কতটুকু। আর আপনি কতটা নিরুপায় হয়েও কিশোরদের জন্য কাজ করেন।,0,celebrity
"ভারত আর ভারতবর্ষের মধ্যে পার্থক্য টা ঠিক বুঝি না, পাকিস্তান বাংলাদেশ যখন ছিল তখন বলা হত ভারতবর্ষ! এখন সব স্বাধীন হইছে, এখনো কি ভারতবর্ষ আছে?",0,celebrity
"আমাদের প্রশ্ন ফাঁস করলো, তখনআপনারা চুপ। আমাদের দ্বিতীয়বারপরীক্ষা দেওয়া বন্ধকরে দিলো তখনো আপনারা চুপ। যতদোষ '১৪ ব্যাচের। '১৪ ব্যাচ চোর, '১৪ব্যাচ হেন, '১৪ ব্যাচ তেন। আপনাদেরকথা শুনলে মনে হত আমরা যেন প্রশ্নফাঁস করতে তাদের বলে দিয়েছি! প্রশ্নফাঁস হলে সেই ব্যাচ যদি চোর হয়তাহলে তো আপনাদের লজিকে এইছোট্ট বাচ্চাগুলাও চোর। কারন তাদেরপ্রশ্নও তো ফাঁস হচ্ছে। এখনআপনারা অনেক কিছুই লিখবেন, বলবেন।কিছুদিন পর সরকারের লোকটাকা দিয়ে আবার আপনাদেরমুখে কুলুপ এটে দিবে। মাঝখানথেকে যত দোষ, যতসমস্যা পোহাতে হচ্ছে '১৪ ব্যাচের।যে দেশে শিক্ষা নিয়ে রাজনীতি চলে সেইজন্মেছি বলতেও আজ লজ্জা লাগে।",0,celebrity
জানাব জাফর তুমি হলে জ্ঞানপাপী ও মূর্খ। বলতে পার তোমার অনেক লেখাপড়া ও ডঃ ডিগ্রী আছে তারপরও ধর্ম জ্ঞান না থাকায় তুমি জ্ঞানহীন।,0,celebrity
"""সবই নোংরা রাজনীতির খেলা """,0,celebrity
আহারে দালালের কান্না!!!,0,celebrity
আমার খালি একটা প্রশ্ন জাফর ইকবাল স্যার এর এত্ত haters কে?🐸,0,celebrity
"পাবলিকের কমেন্ট দেখলেই বোঝা যায়,ডিরেক্ট নৌকায় ভোট চান,পেচানোর কি দরকার আছে? এজন্যই বলি #জাফর_এক_BAL",0,celebrity
"স্যার মারা গেছে আমারে বলিস নাই তো, এসব কিন্তু ঠিক না 😭😭😭😭 Joyoshree Mondal 😥😥😥",0,celebrity
মামুর বেটা তুমি যে ডিগবাজি তা সবাই জানে। এখন আমার হরহর করে বমি আসছে। ওয়াক থু থু,0,celebrity
"স্যার আপনার মত জ্ঞানী ব্যাক্তির কাছে,ছাত্র সমাজ এটা আশা করে নাই।",0,celebrity
লেখা না পড়েই হাহা রিয়েক্ট দিয়ে কমেন্ট পড়তে লাগলাম।,0,celebrity
ভাই নবাব সিরাজ বলেছিল হায়রে অভাগা জাতি,0,celebrity
দুষ্টু রাজায় তুষ্ট প্রজাই রাজাকার,0,celebrity
"আপনার মত  চাটুকারদের মুখে তার কথা মানায় না,  উনি আপনার চেয়ে অনেক উর্দ্ধে",0,celebrity
সার আপনি যা করেছেন ঠিকই করেছেন,0,celebrity
শেষ পর্যন্ত আপনি সময়ের দাবীটা বুঝতে পারলেন এই জন্য কৃতজ্ঞতা জানাচ্ছি। তবে আপনার জন্য যতটুকু শ্রদ্ধা আর ভালোবাসা ছিল তার কোনটাই আর অবশিষ্ট নেই। কেন নেই সেটা আপনি একদিন অন্যকোন বিষয় যেটা 'আপনি ভালো বুঝেন না' তার মাধ্যমে হয়তো বুঝবেন। ভালো থাকবেন।,0,celebrity
"ইহা কলাম নয়, গরুর রচনা হয়ছে। ছ্যার মনে হয় বিটিভি বেশি দেখেন।",0,celebrity
আপনার চেতনায় বোধয় মরিচা ধরে গেছে! তাই এসব বালিয়মার্কা লেখালেখি ছেড়ে দিয়ে আপাতত বিজয়োৎসব করুন।,0,celebrity
আল্লহ  আপনাকে দীর্ঘজীবী করুক।,0,celebrity
স্যার আপনার জন্যে শুভ কামনা রইলো  !,0,celebrity
"আপনারা অযথাই এই মাথামোটা,স্বার্থপর,পা চাটা কুকুর জাফর রাজাকারকে গালি দিচ্ছেন৷ দয়া করে এই বদমাইশটারে কেউ গালি দিবেন না৷ সে দেশের কয়েকটা বুদ্ধি প্রতিবন্ধীর একজন৷ কোটা বাতিল হলে তার মতো অপদার্থের বংশের কারও কোন চাকরী হবে না৷ শালীর বেটি মতিয়ায় সবাইরে রাজাকার কইল,কোন এক ছাত্র তীব্র প্রতিবাদ করল৷ এইটা দেইখা আসল রাজাকার চেইতা গেল?  বাহ শালার রাজাকার মইত্তার রাজাকার জাফর৷৷৷৷",0,celebrity
কোটা সংস্কার  কে কিভাবে কোটা বিরোধি বানাই দিলেন?,0,celebrity
কমেন্ট পড়তে আসলাম 🙊,0,celebrity
ওয়াক থু... মীর জাফর,0,celebrity
শেষের অংশটুকু লিখেই লেখক তার পাঠকদের সাথে রসিকতা করে বসলেন এবং পুরো ঘটনার বর্ণনাটাই মজা আখ্যা দিলেন।,0,celebrity
সহমত স্যার সহমত! আপনি সঠিক বলেছেন! পুরোপুরি সঠিক বস। মুক্তিযুদ্ধের চেতনার দৃষ্টিকোণ থেকে আপনার পোস্ট পুলিতজার প্রাইজের দাবিদার!! এগিয়ে যান বস!!,0,celebrity
"আপনাদের মত কিছু রাজনৈতিক দালাল + বুদ্ধিজীবী যদি দেশে না থাকত, তাহলে দেশের ইতিহাস বছর বছর পাল্টাতো না। আপনাদের ইতিহাস বিকৃতিকারী হিসেবেই পরবর্তী প্রজন্ম মনে রাখবে। আপনি দয়া করে গর্তেই থাকেন।",0,celebrity
Zafar Iqbal Saheb thiki bolechen je nokol baj student-ra konodino chance pabe na,0,celebrity
"আপনাকে গালি দিতেও লজ্জা লাগে।   আপনার বই আমরা তরুনরা সব সময় পড়েছি । এখন আর  পড়া হয় না কারন আপনে নাম্বার ওয়ান দালাল, চুর হেডারপুত",0,celebrity
"বেশ একপেশে ! মুক্তিযুদ্ধ ও মুক্তিযুদ্ধের পক্ষশক্তি বলতে আপনি কী বোঝাতে চান ? ভুয়া মুক্তিযোদ্ধা তৈরি করা, স্বাধীন মতামতহীন ব্যবস্থা, বিচার ব্যবস্থার স্বাধীনতা ধ্বংস, অর্থনৈতিক দূর্বিত্তায়ন— এসব কি মুক্তিযুদ্ধের চেতণার... ?",0,celebrity
"অবশেষে তিনি মর্ত্যে আসিলেন, তিনি তাহাদিগের হালহকিকত স্পষ্ট অবলোকন করিয়া হলেও আসিলেন। অবশেষে তিনি মর্ত্যে আসিলেন।",0,celebrity
মদ খাবেন স্যার?,0,celebrity
শিক্ষার্থীরা ঘৃণা আর ক্ষোভে প্রকাশ্যে অশ্লীল গালি দিচ্ছে!!ছোট ছোট বাচ্চাদের প্রতিবাদের ভাষার কাছে আপনার সুশীলতা হেরে গেছে!!টক-শোতে আপনারা চায়ের চুমুকে সাথে যতটা প্রতিবাদী...বাস্তবের তেল মারামারিতে ততটা প্রতিযোগী!!RIp sir!,0,celebrity
"স্যার, বিনয়ের সাথে প্রশ্ন....  আপনি মুক্তিযুদ্ধের সময় কোথায় ছিলেন?  আপনার বড় ভাই  হুমায়ুন আহমেদ লিখেছেন...  আপনি যাত্রাবাড়িতে আপনাদেরিএক দুসম্পর্কের আত্মীয়ের বাড়ির পেছতে গর্ত করে লুকিয়ে ছিলেন!  আপনার মা তাঁর আত্মজীবনীতে আপনার মুক্তিযুদ্ধে অংশগ্রহণের কোন কথা লিখেন নি।  বেয়াদবি মাফ করবেন...  আপনি মুক্তিযুদ্ধ পেয়েও যুদ্ধে অংশ নেন নি... িআপনার মুখে মুক্তিযুদ্ধ বেমানান।",0,celebrity
"""আগস্ট একটা অশুভ মাস।"" আপনি অনেক বিজ্ঞানমনস্ক স্যার। ❤",0,celebrity
"আমার কষ্টের জায়গা হল আপনি আমার অতি প্রিয় লেখক এবং সত্যিকার দেশপ্রেমিক হুমায়ূন আহমেদ স্যারের ভাই। আপনাকে কটূক্তি করলে স্যারের আত্মা কষ্ট পাবে।যা আমার কোনভাবেই কাম্য নয়।তবে একটা কথা লিখছি আপনি উনার ভাই হবার কোন যোগ্যতা রাখেন না।উনি দলবাজ ছিলেন না,একজন খাঁটি নির্লোভ দেশপ্রেমিক ছিলেন।আল্লাহ উনার সম্মান পৃথিবীতে যেমন দিয়েছেন শেষ বিচারেও দিবেন বলে আমার বিশ্বাস।",0,celebrity
সে যে জ্ঞান পাপী সেটার প্রমাণ নিরন্তর দিয়েই যাচ্ছে! আল্লাহ তারে কিছু শুভ বুদ্ধি দান করুন!,0,celebrity
কোটা সংস্কার আন্দোলন না হলে যেমন জানা যেত না এদেশের নামসর্বস্ব প্রাইভেট বিশ্ববিদ্যালয়ের ছাত্ররাও মেধাবী তেমনি আপনার লেখা এফ বি তে না আসলে জানা হত না বিরোধী মতের পাঠকেরা ও লেখাগুলো নিয়মিতই  পড়ে।,0,celebrity
জাজাকাল্লাহু খাইরান 😍😍😍😍,0,celebrity
বিরক্তিকর যাহ😃,0,celebrity
আমাদের দেশের শিক্ষাব্যবস্থা যদি দলীয় রাজনীতি মুক্ত হতো তাহলে দেশের শিক্ষার মান বাড়তো।,0,celebrity
চুরি করে কল্প বিজ্ঞান লেখেন সেটাই ভাল। দেশে ধর্ম নিয়ে রাজনীতি করলে সেটা হয় ধর্ম ব্যবসা আর মুক্তিযুদ্ধ নিয়ে রাজনীতি করলে সেটা ব্যবসা হয় না। দেশের মানুষকে স্বাধীনতার ৪৭ বছর পর এসেও বিভাজন করে নিজের স্বার্থ আদায়ের জন্য আজ আপনারাই ঘৃণ্যিত। এদেশের মানুষ বিভাজন চায় না শান্তি চায়। যুদ্ধের পর এতো বছর কি করছিলেন? এতো দেশপ্রেমিক যদি হয়ে থেকেছিলেন তাহলে যুদ্ধের সময় অস্ত্র হাতে নিতে যদি না পেরে থাকেন যুদ্ধের পরে কি করছিলেন তখন তো রাজাকার বধ করতে পারতেন। নাকি তখন রাজাকাররা মেশিনগান হাতে নিয়ে দেশে ঘুরছিলো। আর যেহেতু কিছুই করতে পারেননি তাই আপনার মুখ থেকে নষ্ট দেশপ্রেমিক সাজা দেখতে চাইনা। যদি পারেন কিভাবে দেশকে প্রযুক্তিগতভাবে এগিয়ে নেয়া যায় সে চেষ্টা করুন। আপনাদের স্বার্থের বিষ এই তরুন প্রজন্মের মধ্যে ঢুকিয়ে দেশের মানুষকে বিভাজন করবেন না। মনে রাখবেন এখন প্রজন্ম শুধু দেশ নয় সারা পৃথিবী নিয়ে গবেষণা করে তাই আপনাদের যুগের চেয়ে শতগুণ এগিয়ে আছে এ প্রজন্ম।,0,celebrity
লোকটা আবারও ট্রেঞ্চ খুঁড়ে বের হয়েছে!,0,celebrity
"অনেক দিনের ইচ্ছে, আপনার সুদীর্ঘ দিনের পরম যত্নে গড়ে তোলা নীড়+মল (মলের নীড়) গোফের উপর হড়হড় করে বমি করি।",0,celebrity
"কোটা আন্দোলন কে বিশেষ গুরুত্ব দিয়ে স্যার লিখেছেন, এক কথায় কোটা আন্দোলনকারী রা সবাই জামাত বিম্পি, এইটা ঘুরিয়ে পেচিয়ে তিনি পরিস্কার করে বলে দিয়েছেন, তারা যে তারুন্যের ইশতেহার দিয়েছেন, সেটাকে ঘুরিয়ে পেচিয়ে জামাত বিম্পির ইশতেহার বানিয়ে দিলেন,   তাদের আন্দোলনের সফলতা কেও স্যার স্বীকার করে নিয়েছেন, ধন্যবাদ স্যার, এই সত্য স্বীকার করার জন্য। এর মানে দাড়ালো ন্যায্য অধিকারের বেলায় সকল আন্দোলন জন সমর্থন পায়।  সেটা জামাত বিম্পি করুক, আর আওয়ামীলীগ করুক।   জন সমর্থনবীহিন আন্দোলন করে জামাত বিম্পিও যেমন সফলতা পায়নি। তেমনি জনসমর্থনহীন লেখা লিখে অনেক লেখক ই আস্তাকুরে চলে যাবে কালের বিবর্তনে।",0,celebrity
আমরা আপনাকে ভালোবাসি💜 ফিরে এসেছেন এটাই শুকরিয়া😊,0,celebrity
কমেন্টে পড়তে আইছি৷ 😎😎😎,0,celebrity
"দীর্ঘ জার্নির পর প্রচুর প্রশ্রাবের চাপ ছিল,পকেটে ভাংতি টাকা না থাকায় একটা টয়লেটেও প্রশ্রাব করতে দিলনা,আন্নের ইষঠেঠাস পড়ার পর ব্যবস্থা হয়েই গেলো অবশেষে আন্নের প্রোপাইল ভরে মুতেই দিলাম আহ্ শান্তি......😹🔫",0,celebrity
উনার অসুবিধাটা কেউ দেখলো না  :-D,0,celebrity
"আমার এ দেশ কখনো ওদের চিন্তার মত মৃত্য দেশ হতে পারে না। যত বাধাই আসুক, এগিয়ে যাবে, এগিয়ে যাচ্ছ। আর আপনার সময় উপযোগী লেখার জন্য ধন্যবান।",0,celebrity
কিছুই  বুঝলাম না আপনারা মানে স্যার আপনি আর আয়মান সাদিক এত্তদিন পর আবার দুজনই একই দিনে এসব নিয়ে কথা বলতেছন!!!😂😂😂সব ঠিক আছে তো!!!,0,celebrity
পোষ্ট পড়া লাগবে না কমেন্ট পড়েন Jannatul Maysa,0,celebrity
অসাধারণ প্রস্তাবনা স্যার!😖😖😖,0,celebrity
"স্যার আপনার অসহায় বোধ করার কোনো কারন নেই।আপনিতো সরকারের পা চ্যাটা গোলাম, গোলামি চালিয়ে যান। 😂😂",0,celebrity
যাক অবশেষে দলমত নির্বিশেষে মোটামুটি সবাই একমত যে এই লোকটা ফালতু প্রকৃতির লোক।,0,celebrity
রাজাকারের  বাচ্চাগুলো কেনো যে এখানে  অাসে?? মনে হয় পাকির রক্তের প্রতিশোধ নিতে চায়?,0,celebrity
যুদ্ধের সময় পালিয়ে বেড়ানো লোকের মুখে মুক্তিযুদ্ধের চেতনার কথা খুব একটা মানায় না।,0,celebrity
আপনি যে  ট্যাগ লাগানো গাছ বলদ  তা আর প্রমাণ করতে আসবেন না।।। আপনি যা বলছেন নিজেই জানেন না কি সব বলতেছেন।।পাগল হয়ে গেছেন।।আপনি ট্রল আর সিরিয়াস নেন্স কি তাই বুঝেন না।।আপনি আসলে ননসেন্স,0,celebrity
"মুক্তিযুদ্ধ এবং মুক্তিযোদ্ধারা আমাদেরও অহংকারের যায়গা। খুব ভালো লাগলো লেখাটা,এ ধরনের লেখা সব সময়ই পড়া যায়।",0,celebrity
মি জাফর কোথায় আপনাদের তথাকথিত নারী নেতারা আর আপনি এতদিন কোথায় ছিলেন,0,celebrity
"আপনার মরে যাওয়া উচিত।আপনি কি এখনো ঘুমে আছেন?হা হা রিয়েক্ট, কমেন্টস পড়েতো বোঝা উচিতযে তেল ব্যবসা বন্ধ করতে হবে।আপনি একাডেমিক শিক্ষক হিসেবে সম্মানীয় কিন্তু মানুষ হিসেবে জঘন্য।",0,celebrity
আমার মেইন আইডি ২ বছর আগে যৌক্তিক কমেন্ট করার কারনে আপনি বল্ক করেছেন। কিন্ত আজকে যে আপনাকে পোলাপাইন  চুইদা তাল গাছে তুলতেছে এখন কি করবেন।  তুই তাল গাছেই বসে থাক মাদারচোদ। নিচে নামলে এবার তোরে বাইন্দা কুর্তা দিয়া চোদামু দালালের বাচ্চা।,0,celebrity
স্যার আপনার জন্য দোয়া আছে।আপনি ভালো হোন এই দোয়া করি।,0,celebrity
এই আবালের লেখাটার একটি লাইনও না পড়ে সরাসরি কমেন্টে চলে আসলাম। আসার পর মনে হলো ভুল করিনি।😂,0,celebrity
২০০৮ থেকে ২০১১ পর্যন্ত হুবুহ কিছু প্রশ্ন physics plus ও math plus নামক গাইড থেকে এসেছে।এমনকি সেখানকার এক বড় ভাই বলেছিলেন ঐ সব গাইড ফলো করলে নাকি ঢাবিতে চান্স পাওয়া আমার জন্য সহজ হবে।কারণ হিসেবে তিনি বলেছিলেন প্রথমবার তিনি শুধু বই পড়ে গিয়ে চান্স পাননি কিন্তু পরেরবার তিনি ঐ গাইড গুলো 'ফলো' করে চান্স পান।ঢাবির ভর্তি পদ্ধতি যে কতটা অস্বচ্ছ তা প্রমাণ করে যে তারা ইন্টারে যেসব বিষয় পড়া হয়নি সেসব বিষয়ের উপর প্রশ্ন করে যাতে তারা সাধারণ ছাত্রদের আটকাতে পারে।তাছাড়া অনেকেই আছে যারা প্রথমবার চান্স পায় না কিন্তু দ্বিতীয়বার তারা ঠিকই চান্স পেয়ে যায়।এতেও মেধার প্রকৃত যাচাই হয় না।কারণ এক ব্যাচ তিন মাস সময় পাচ্ছে আর আরেক ব্যাচ পায় বারো মাস।,0,celebrity
"আমার খুব জানতে ইচ্ছে করছে মহান মুক্তিযুদ্ধের সময় জাফর ইকবাল দেশের জন্য কি করেছেন??ওনার তো যুদ্ধে যাওয়ার মত বয়স ছিল,,",0,celebrity
জুহী আনজুম মেধা 😍 পড়,0,celebrity
আপনি পচে গেছেন। বার বার কোটা নিয়ে ভিন্ন ভিন্ন ভাবে ছাত্রদের বিরুদ্ধে পুরো বিষয়টা  না জেনে লিখে সরকারের দালালি করছেন। মতিয়া আপার বক্তব্য এর প্রতিবাদ করাতে আপনার ভালো লাগল না। ফালতু দালাল কোথাকার,0,celebrity
"আর কত দালালী করবেন স্যার,পেশাটাই হয়ে গেছে আপনাদের এখন দালালী,অসৎ লোকের কারনে সমাজ ধংস হয় না সমাজ ধংস হয় ভালো মানুষের নীরবতায়।",0,celebrity
কি মুশকিল! কই ছিলেন প্রিয় স্যার????,0,celebrity
আল্লাহ আমাদেরকে হেফাজত করুন। আমিন।,0,celebrity
মানুষ এতই ঘৃণা করে এই দালাল স্যার কে ???,0,celebrity
শুনলাম উনি ফেসবুক ইউজ করেন নাহ তাহলে এই লিখা কে লিখলো ??,0,celebrity
জানাজার সময় মুখ খুল্ল লাশ...,0,celebrity
নতুন কোনো গল্পের বই ভাব্লাম। না স্যার এ বই বাজারে উঠবে না। বাড়ি রেখে দিন!   কলের গান শোনাতে আসছে!,0,celebrity
"স্যার কোটা সংস্কার নাইবা চাইলেন  কিন্তু অদ্ভূত লেখনী বা ভালো কাজ  কি অস্বীকার করা যায়।সবার খেয়াল রাখা উচিৎ উনি একজন শিক্ষক, শিক্ষক কে অপমান করে কি প্রগতিশীল হওয়া সম্ভব তবে বিশেষ ছাত্র সংঘটন আর সাধারণ ছাত্র এর মধ্যে পার্থক্য কই রইল।যেভাবে সবাই অপমানজনক ঢালাও বক্তব্য দিচ্ছেন এটা বাঞ্ছনীয় নয় অন্তত কোটাসংস্কার গ্রুপের সদস্যদের।আরো নমনীয় ধৈর্যশীল হতে হবে সকল কে।ভিন্নমত থাকবেই।",0,celebrity
ধন্যবাদ,0,celebrity
"আস্তাগফিরল্লাহ স্যার,ইংরেজী নববর্ষেরর শুভেচ্ছা দিচ্ছেন বাংলায়!!আপনারা পিএইচডি করা লোক এটা করতে পারেন? ওও, আপনারা তো সব পারেন আবার।কারণ আপনারা চেতনার লোক।",0,celebrity
আমি জাফর স্যারে এই লেখাটা পড়ছি।,0,celebrity
ধর্ম কিংবা কমিউনিজম নিয়ে কোনো ইস্যু হলে এই জাফ্রিকবালের মতো দালালদেরই সবার আগে পাওয়া যাবে।,0,celebrity
দেশ নিয়ে একদম দুশ্চিন্তা করবেন না। বরং নিশ্চিন্তে থেকে পশ্চিমাদের খারাপ ধারনাকে মিথ্যা প্রমাণ করুন।,0,celebrity
আবেদ চৌধুরী! আমি গর্ব করি!!,0,celebrity
"বিশিষ্ট গর্ত বিজ্ঞানী এবং মুক্তিযোদ্ধা তিনি,,তাকে নিয়ে বাজে কথা বললে চাকরি থাকবে না বললাম,,,,,",0,celebrity
স্যার কি ভোট দিয়েছিলেন?????নাকি আপনার ভোটও আমাদের মত অস্রের মুখে জিম্মি করে কেড়ে নেওয়া হয়েছে?????  নাকি আমার চোখের সামনে ঘটে যাওয়া ৭০ বছরের বৃদ্ধের গালে ১৭ বছরের ছেলের চপেটাঘাত।  নাকি সামান্য কিছু ভোটের জন্য ভোট কেন্দ্রের চারিদিকে বোম্বিং করে আতংক তৈরি করেছিল।  স্যার এর কোনটাই মিথ্যা না।আমার চোখে দেখা ঘটনা। আমি দীর্ঘ পথ পাড়ি দিয়েছিলাম ভোট টা দেব বলে তাই বলে এভাবে ভোট ডাকাতি করবে আপনার ধারনকৃত চেতনাধারী রা।  স্যার সৎ সাহস আছে কি বলার নীতি নৈতিকতা নিয়ে কথা বলার।জানি নেই কারন আপনি তো কাউকে না কাউকে প্রতিনিধিত্ব করেন আমাদের মত সাধারন মানুষের না।।।।।।  নীতি কথা তার মুখে মানায় যিনি সকল পরিস্থিতিতে আমাদের মত সাধারণ মানুষের কথা বলে। ভাল থাকবেন স্যার  অসাম্প্রদায়িক বাংলাদেশ আপনি যেমন চান আমরাও চাই কিন্তু সেটা এভাবে না স্যার।,0,celebrity
চামচামি আর কত,0,celebrity
বিশ্বাস করেন স্যার সারাটা সপ্তাহ আপনার বিনোদন মার্কা পোষ্টের জন্য সকলেই অপেক্ষা করে। শুধুমাত্র মন খুলে হাসবে বলে,0,celebrity
আপনার মতো চরিত্রহীনের কাছ থেকে এর চেয়ে বেশি আর কি আমরা আশা করতে পারি ?,0,celebrity
আপনিও কী আয়মান সাদিক হতে চান?? 😃,0,celebrity
ইনশাল্লাহ স্যার আপনি দ্রুত সুস্থ হয়ে যাবেন।,0,celebrity
"স্যার, দ্বিতীয় মুক্তিযুদ্ধ এখনও শেষ হয়নি। আপনি এর আগেই গর্ত থেকে বেরিয়ে পড়লেন কেন? খুব বেশিই বমি পেয়েছিল?",0,celebrity
সেকেন্ড টাইমার দের কি হবে? 😒😒,0,celebrity
তীব্র নিন্দা জানাচ্ছি আপ্নার খোলা চিঠি এর প্রতি।,0,celebrity
মি: জাফর মনে হয় এবার এমপি ইলেকশনে খাড়াইতে চাচ্ছেন।,0,celebrity
স্যার কে নিয়া বাজে কমেন্টস করতে খারাপ লাগে না আপনাদের।আগে জাফর ইকবাল হওয়ার ক্ষমতা অর্জন করেন তারপর স্যারকে নিয়ে বাজে কমেন্টস করবেন।,0,celebrity
শেয়াল সবসময় চায় মুরগীর স্বাধীনতা.. কারন মুরগী স্বাধীন হলে সে তার ইচ্ছামত ভোগ করতে পারবে.. আর আপনাদের মতো মানুষরূপী আফ্রিকার ষ্যাড়েরা চায় নারীদের স্বাধীনতার নামে অবাধে চলাফেরা করা.যাতে করে আপনারা ইচ্ছামত নারীদের ভোগ করতে পারেন..,0,celebrity
স্যারের ঘুম ভেঙেছে।,0,celebrity
৩০ তারিখে হুমায়ূন আহমেদ স্যার এসে যে আপনার ভোটটি মেরে দিল। আপনি নৌকা নৌকা করে গিয়েও ভোট দিতে না পেরে চলে আসলেন।  এটাকে আপনি কিভাবে দেখেন স্যার?,0,celebrity
"চেতনা বিক্রি করে আর কত খাবেন,এবার একটু থামেন।আর ঐ যে বললেন না,যে চেতনার চশমা পরেন আসলে পরেন তো কাঠের চশমা।তাই কিছু দেখেও দেখেন না। আপনার বাবা মুক্তিযোদ্ধা, মা ভালো মানুষ,ভাইগুলাও ভালো, কিন্তু আপনি এমন তৈলবাজ ক্যান??আবার বুদ্ধিজীবি  *দায়😁😁",0,celebrity
উনি সম্ভবত এফবি পাসওয়ার্ড ভুলে গেছিলেন.তাই এতোদিনে স্ট্যাটাস টা দিতে পেরেছেন...শুধু শুধুই ভুল বুঝা হচ্ছে....😫😫😫😫😫😫🙈🙊🙉,0,celebrity
"আপনার শাস্তি এটাই স্যার, সামনে বছর দেখবেন সব বোর্ডে সবাই পাস!! আরো হতে পারে সবাই জিপিএ ফাইভ বা গোল্ডেন ফাইভ!! মরার দেশ!!",0,celebrity
গলা ব্যথা করলে আমার কিন্তু দোষ নাই  Arifa Sanzida Zebin,0,celebrity
" জীবনে চলার পথে , রাস্তার মধ্যে বহুত কুকুর অকারণে ঘেউ ঘেউ করবে। সবাইকে যদি ঢিল মারতে মারতে যাও,তাহলে গন্তব্যে পৌঁছুবে কখনো ??    Iqbal sir , Ignore themselves . .",0,celebrity
কমেন্টগুলা পইড়া মুই তো চিৎ হই গেসিগা!,0,celebrity
কিছু কিছু মানুষের পোষ্ট চেকই করা হয় কমেন্ট দেখার জন্য।তবে এসব বক্তৃতা তো পাব্লিক খায় না।নতুনত্ব দরকার😂,0,celebrity
"আপনার সুশীলগিরি যে দালালি সেটা সবাই জানে। পেট্রোল বোমা সহ কারা ধরা পড়ে সেটা আপনি দেখবেন না। কারণ কোন মিড়িয়া সেটা দেখাতে পারবেনা। অনলাইন পত্রিকাতেই সীমাবদ্ধ থাকবে। ভোটাধিকারের কথা বলুন। সবার মত প্রকাশের ব্যবস্থা করুন। মহিলাদের গ্রেফতার করা হচ্ছে কোন অপরাধে? তারা তো রাজনীিত করেনা। আপনি বিচার বহির্ভূত হত্যাকান্ডের বিরুদ্ধে বলুন। আপনার তো সেই চক্ষু নাই। আগুনে পুড়লে কষ্ট লাগে কিন্তু পঁচিশটা গুলি করে হত্যা করা কাউন্সিলরের মৃত্যুু আপনাকে নাড়া দেবেনা। বিশ্ব ইজতেমার জন্য মনকাঁদে কিন্তু হেফাজতের জন্য ঠোঁটে ক্রুর হাসি ফোটে। আপনি বুঝেও না বুঝার ভান করতে পারেন, কিন্তু প্রতিটি মানুষ আজ রাজনীতি নিয়ে ভাবে।",0,celebrity
স্যার যহুরের নামাজ পড়েছেন!😆😆😆😆😂😂😂,0,celebrity
সম্ভাবনা উজ্জ্বল।,0,celebrity
চেতনা ব্যবসায়ী,0,celebrity
স্যার আপনি ঠিক আছেন শুনে অনেক খুশি হয়েছি.... সেদিন যদি আপনার কিছু হয়ে যেত আমি আমার প্রিয় লেখককে হাড়িয়ে ফেলতাম... আপনার বই আমাকে অনেক অনুপ্রাণিত করে... উৎসাহ দেয়... আপনার বই থেকে অনেক কিছু জেনেছি... শিখেছি... আল্লাহর অশেষ রহমত আপনি ঠিক আছেন... 😊😊😒,0,celebrity
"তুমি বাঁইচা আছো,,",0,celebrity
আমাকে একটু ক্লিয়ার করেন স্যার এটা কি সাইন্স ফ্রিকশান ছিলো?,0,celebrity
"বামাতি ভাইজানেরা আপ্নারা নিজেদের হোগা দিয়া আগে হাগার অভ্যাস করুন, তারপর জাফর স্যারের লেখার সমালোচনা করবেন।",0,celebrity
"পেজ_ হ্যাক হইছে সিওর! নাইলে মৃত মানুষ ক্যামতে স্ট্যাটাস_দেয়""!!__😜😂",0,celebrity
আমনের ও হবে,0,celebrity
"""অসমাপ্ত আত্মজীবনী- জাতির জনক বঙ্গবন্ধু শেখ মুজিবর রহমান""    ২০০৪ সালে শেখ মুজিবুর রহমানের লেখা চারটি খাতা আকস্মিকভাবে তাঁর কন্যা শেখ হাসিনার হস্তগত হয়।  খাতাগুলি অতি পুরানো, পাতাগুলি জীর্ণপ্রায় এবং লেখা প্রায়শ অস্পষ্ট। মূল্যবান সেই খাতাগুলি পাঠ করে জানা গেল এটি বঙ্গবন্ধুর অসমাপ্ত আত্মজীবনী, যা তিনি ১৯৬৭ সালের মাঝামাঝি সময়ে ঢাকা সেন্ট্রাল জেলে অন্তরীণ অবস্থায় লেখা শুরু করেছিলেন, কিন্তু শেষ করতে পারেননি।  জেল-জুলুম, নিগ্রহ-নিপীড়ন যাঁকে সদা তাড়া করে ফিরেছে, রাজনৈতিক কর্মকাণ্ডে উৎসর্গীকৃত-প্রাণ, সদাব্যস্ত বঙ্গবন্ধু যে আত্মজীবনী লেখায় হাত দিয়েছিলেন এবং কিছুটা লিখেছেনও, এই বইটি তার সাক্ষর বহন করছে।  For PDF Download >>> http://www.liberationwarbangladesh.org/2014/05/blog-post_26.html",0,celebrity
"আচ্ছা, জাফর ইকবাল স্যার কই?  শুনলাম, তিনি নাকি লক্ষ কোটি ছাত্রদের হৃদয়ের স্পন্দন!  ছাত্ররা বাসের চাপায় মারা যাচ্ছে, ট্রাকের নিচে পিষ্ট হচ্ছে, পুলিশের গুলিতে আহত হচ্ছে। এসব কি তিনি দেখেন না?  শুনলাম, তিনি নাকি সুশীল? তিনি নাকি বুদ্ধিজীবী?  অথচ তিনি ছাত্রদের পক্ষে একটা কথাও বললেন না,  একটা বিবৃতি ও দিলেন না!  ফেসবুক পেইজে একটা স্ট্যাটাস ও দেন নাই!  নাহ, জাফর ইকবাল লক্ষ কোটি ছাত্রদের হৃদয়ের স্পন্দন হতে পারেন না, সুশীল হতে পারেন না, বুদ্ধিজীবী হতে পারেন না।  তিনি মানবতার দুশমন,  ছাত্রসমাজের দুশমন, কুশীল, সুবিধাবাদী! ধিক্কার জানাই জ্ঞানপাপী মীর জাফর ইকবাল কে। থুঃ।  জাফর ইকবাল কোন চ্যাটের বা*?",0,celebrity
"এই দেশে 'মীর জাফর' গালির মতো হয়তো 'জাফর ইকবাল' টাও আপনার মতো কপট  সহজ-সরল লোকের কারনে জনপ্রিয় গালি হবে। আপনি রাজনীতি বোঝেন না, তেলবাজিটা ভালোই বোঝেন!!",0,celebrity
এনার মাথার আসলে সমস্যা আছে। অতি দ্রুত পাবনায় পাঠানো দরকার।,0,celebrity
দোয়া করি সুস্থ হয়ে ইসলামের দিকে ফিরে আসবেন। নাহলে যে অনন্তকাল জাহান্নামের আগুনে পুড়বেন। আমি চাইনা আপনি আগুন 🔥 এর দিকে যান। সামান্য সার্থে।,0,celebrity
"*********** আপনি কি মুক্তিযুদ্ধের সপক্ষ শক্তি....? ************  “তাহলে সরকারকে বিব্রত করবেন না...  ধরুন আপনাকে ডিবি পুলিশ কোন কারণ ছাড়াই তুলে নিয়ে হাড্ডি ভাঙ্গা পিটানি দিয়েছে। এমতাবস্থায় ঘুণাক্ষরেও চিৎকার করে কান্না করে সরকারকে বিব্রত করবেন না। কারণ তাতে জামাত বিএনপি ক্ষমতায় চলে আসবে। চুপ করে ভাল ছেলেটির মত হাসিমুখে পেটানি সহ্য করুন। জামাত বিএনপি আসলে কিন্তু আরো মারতো। সেটা থেকে রক্ষা পাওয়ার জন্য জননেত্রী শেখ হাসিনাকে ধন্যবাদ জানাতে ভুলবেন না।   ধরুন আপনাকে ছাত্রলীগ রাস্তায় ফেলে হাত ভেঙ্গে দিয়েছে। আপনি চেঁচিয়ে উঠবেন না। মহান মুক্তিযুদ্ধে ছাত্রলীগের অবদানের কথা ভেবে হাসিমুখে ভাঙ্গা হাতটি নিয়ে দৌঁড়ান। বেঁচে ফিরতে পারলে ছাত্রলীগের সুনাম করে ফেইসবুকে একটি পোস্ট দিতে ভুলবেননা। মনে রাখবেন, বিএনপি জামাত হলে আপনার দুটো হাতই ভেঙ্গে দিতো। ছাত্রলীগ তো অল্পের ওপর একটি হাত ভেঙ্গেছে। ছাত্রলীগকে ধন্যবাদ দেয়া আপনার চেতনাগত দায়িত্ব।   ধরুন আপনার ভাইকে র‍্যাব ধরে নিয়ে দশ লাখ টাকা চেয়েছে। না দিলে তাকে ক্রসফায়ারে মেরে দেবে বলে হুমকিও দিয়েছে। আপনি সেটা আবার সাংবাদিকদের কেন বলবেন? সরকারকে বিব্রত করতে চান? চুপ থাকুন। মুক্তিযুদ্ধের পক্ষে থাকুন। দশ লাখের চেয়ে মুক্তিযুদ্ধ অনেক বড়। ভাইটিকে ফিরে না পেলেও বেশি কথা বলবেন না। মনে রাখবেন, স্বাধীনতার সপক্ষের শক্তি ক্ষমতায়। বিএনপি জামাত আসলে আরো অনেক কিছু হতে পারতো। সেসব ভেবে আওয়ামী লীগকে পরেরবার ভোট দিন। মুক্তিযুদ্ধের চেতনার সাথে বেইমানি করবে না।   ধরুন আপনার বোনটিকে কোন আওয়ামী নেতা তুলে নিয়ে গেছে। বেশি বাড়াবাড়ি করবেন না। তাতে মুক্তিযুদ্ধের চেতনা ক্ষতিগ্রস্ত হবে। অপেক্ষা করুন। বোনটিকে ফেরত দেয় কিনা। ফেরত দিলে ভাববেন, বিএনপি জামাত ক্ষমতায় থাকলে তো বোনটি ফেরতই আসতো না। ভাগ্য ভাল, বোনটিকে আওয়ামী লীগ নেতা নিয়েছিল। তাই ফেরত পেলেন। মুক্তিযুদ্ধের সরকার, স্বাধীনতার সপক্ষ শক্তি আছে বলেই এমনটি হলো। তাই বেশি ট্যাঁ ফুঁ করবেন না। আর বোনটিকে যদি ফেরত না পান, ভাববেন, অন্য বোনগুলো তো অক্ষত আছে। বিএনপি জামাত থাকলে সবাইকেই তুলে নিতো। এই ভেবে দেশনেত্রী শেখ হাসিনাকে ধন্যবাদ দিন। উনি আছেন বলেই এক বোনের ওপর দিয়ে গেছে। উনি না থাকলে সবগুলো বোনকেই নিয়ে যেতো। মুক্তিযুদ্ধের সপক্ষ শক্তি বলে কথা।   সরকারকে বিব্রত করবেন না। মুক্তিযুদ্ধের পক্ষে থাকুন। স্বাধীনতা বিরোধীরা নইলে চলে আসবে। তাই পরেরবার অবশ্যই আওয়ামী লীগকেই ভোট দিয়ে জয়যুক্ত করুন। অবশ্য কেউ ভোট না দিলেও তারাই জয়ী হবে। সেসব নিয়ে আপনি টেনশন নিয়েন না। মনীষা চক্রবর্তী বরিশালে ইলেকশন করেছিল, ভোট দিতে গিয়ে দেখেছে সব ব্যালটে নৌকায় সিল দেয়া। আপনি ভোট দিতে না গেলেও মুক্তিযুদ্ধের শক্তি আপনার ভোটটি দিয়ে দেবে। কী লাভ এত কষ্ট করে কেন্দ্রে গিয়ে ভোট দেয়ার? ভোট দিতে গিয়ে সরকারকে বিব্রত করবেন না। সরকার আপনার কষ্টের কথা ভেবে নিজেরাই ভোটটি দিয়ে নেবেন।   সরকারের প্রশংসা করুন এবং জীবিত থাকুন।  বলা তো যায় না...”",0,celebrity
"Wishing a very happy birthday to you, honorable sir.",0,celebrity
"আপনার লিখা এখন পড়ি না, কমেন্ট পড়ি আর হা হা রিয়াক্ট দেই সেই কোটা আন্দোলনের পর থেকে",0,celebrity
শেষ পর্যন্ত তুই ও পা চাটার দলে,0,celebrity
@ মৌসুমী মন খারাপ করেন  না। জানোয়ার না থাকলে মানুষ চিনবেন কি করে? হাহাহা,0,celebrity
বিএনপি-জামায়ত অাসলে হিন্দুদের কপালপোঁড়ে মানলাম! অাঃলীগ অাসলে মুসলিমদের কি উপকার হয় একটু ক্লিয়ার করে বলবেন কি???,0,celebrity
আহা,0,celebrity
you are right sir,0,celebrity
এটা কার বই থেকে কপি বা অনুবাদ করা জানাবেন পিলিগ! যেখানে সেখানে মানবতা পুন্দান কেরে?,0,celebrity
আমাদের মাঝে সুস্থ হয়ে ফিরে এসেছেন এর চেয়ে বড়কিছু আর কি হতে পারে!😊,0,celebrity
"এই জাতীয় সংগিত আর জাতীয় পতাকার প্রতি ভালোবাসার কথা অন্তত আপনার মুখে মানায় না স্যার।এগুলো শুধুই ভন্ডামি।আপনি কাল্পনিক চরিত্র তপুকে নিয়ে অনেক কষ্ট প্রকাশ করে লিখতে পারেন, কিন্তু কোটা আন্দোলনকারি তরিকুলরা যখন হাতুরিপেটা হয়ে হাসপাতালে চিকিত্‍সাটুকু না পাওয়ার মত অমানিবিকতার স্বিকার হয় তখন আপনার কষ্ট হয় না,তাদেরকে নিয়ে লেখার রুচি হয় না অথচ আপনি দেশকে ভালোবাসার দাবি করেন।",0,celebrity
"DEAR SIR, আপনার মিনতিভরা লেখা পড়ে কারো বোধোদয় ঘটবেে এমনটা আশা এখনও যদি আপনার মনে থেকে থাকে তবে আগামী গণিত পরী: পর আশা করি থাকবেনা। কারণ নিম্ন লিখিত---   গণিত...  ***৩ নং ২টি গরু ও ১টি খাসির মুল্য একত্রে ৭০০০০ টাকা।১টি খাসির মুল্য ৭৫০০ টাকা (ক)৩টি খাসির মুল্য কত? (খ)১ টি গরুর মুল্য কত? (গ) ১টি গরুর মুল্য ও ১টি খাসির মুল্য কত? (ঘ)১টি গরুর মুল্য দিয়ে কয়টি খাসি পাওয়া জাবে? ***৫নং ২০১৩ সালে সমাপনি পরিখায় বি,জি,বি সরকারি প্রাথমিক বিদ্যালয়র ১ থেকে ৮ নম্বর শিখাদের গনিত বিসয়ের প্রাপ্ত নম্বর।১২,৯০,৯৪, ৮৮,৯০,৪৪,৮০,৮২ (ক) ১ম চার জন শিখাথির গর কত? (খ)সেস ৩জন শিখাথির গর নম্বর কত? (গ)১ম চার জন শিখাথির গর ও সেস ৩জন শিখাথির গড়ের প্রাথক্য কত? (ঘ)শিখাথির গড় নম্বর কত? ***৫টি - নম্বর অনুশিলনি-৫ ৫ নম্বর অনুশিলনি-৭(ঘ) ১৫ নম্বর অনিশিলনি-৮(খ) পৃষটা ৮৫- ১২ নম্বর অনুশিলনি-৯ পৃ :৯০- ২১ নম্বর পৃ: ১১১ উদাহরন -৯ ***জ্যামিতি ক) ৩ সে,মি ব্যাসাধের একটি বৃতত আক এবং এর ব্যাস ও ব্যাসাধ ও জ্যা চিহিনত কর। খ) সামানতরিক, সুষমকোন  বাকি প্রশ্ন আসছে... লাইক কমেন্ট শেয়ার না করলে পরবর্তী পোস্ট করা হবে না..",0,celebrity
"খাটাশ কে খাটাশই বলতে হয়, খাটাশ কে ভদ্র ভাবে ডাকতে গিয়ে বিড়াল ডাকলে তো হবে না। জাফর ইকবাল এই দেশের তরুনদের সাথে বিশ্বাসঘাতকতা করেছে, যেই তরুনদের কষ্টে যোগাড় করা টাকায় তার পোলা মাইয়া বিদেশ পড়ালেখা করে, সেই তরুনরা যখন তার কাছ থেকে একটুখানি মানসিক সাপোর্ট চাইছিলো মাত্র, তখন সে তাদের গায়ে হড়হড় করে বমি করে দিয়েছিলো, ওরে সকাল বিকাল নিয়ম করে গাইলানো সওয়াবের কাজ!",0,celebrity
ইকুইলিব্রিয়াম দরকার।কিভাবে সম্ভব?আমার কাছে কোন শক্তি নাই।উপরের দিকে তাকাই আছি।,0,celebrity
বদ লোকের কাজ সমালোচনা করা।তারা দুই পাতা লিখতে না পারলেও চার পাতা জ্ঞান ঠিকই দেবে।স্যার বিচলিত হবেন না।আমি আপনার কথার সাথে একমত ছিলাম আছি আর থাকব!,0,celebrity
"স্যর আপনার লজ্জা বলতে নেই লজ্জা থাকলে কখনো ফেইসবুকে গাদার মতো বকবক করতেন না, আর জারজ এর সাথে আপনার নামের সাথে মিল খুজে পাওয়া যায়।",0,celebrity
জনাব জাফর ইকবাল স্যার  আপনি অনেক বিজ্ঞ একজন লোক কিন্তু সব বিসয়ে নিজের অধিকার ফলানো  ভাল দেখায় না। আপনার ২০১৮ সালের physics and chemistry বই তা কি জগাখিচুরি বানাইছেন।। আমদের মত ছাত্রদের আজকে এইজন্নই প্রাইভেট পরতে জাইতে হয়.।  আপনি যদি বই গুলা তে details দিয়ে দিতেন তাহলে আর গাইড কিনতে হইত না। আগের বইগুলা অনেক ভাল ছিল। অইগুলা থাকলে অনক ভাল হইত আমদের জন্য,0,celebrity
লিস্টের সবার কমেন্টে হাহা দিতে আসছি । এক বালের পোস্ট পড়িনাই। তো আমারে কি বাস চাপা দিয়া মাইরা ফালাবে?😭😭😭,0,celebrity
স্যার এই বাঁশ টা না দিলে হয়না?,0,celebrity
শেখার অাছে অনেকে,0,celebrity
আমাদের সায়েন্স ফিকশন লেখক জাফর ইকবাল স্যারের পাবলিক ফিগারের  এই অবস্থ।।  কমেন্ট গুলো পড়ো।। Tarek Ahmed Zibal Muzahid Rana Pankaj Kumar Paul Bigwig Nafish Ismail Mijan Tanim Shawon Rafsan Sakib মোঃ জাহিদ হাসান,0,celebrity
"আমাদের সম্মানিত জাফর ইকবাল স্যার আপনার প্রীতি পূর্ন সম্মান রেখেই বলছি আপনার লাভ আছে, আপনি ঢাকায় আসেন। এরাই কিন্তু আপনার সাইন্স ফিকশন পড়ে । বইয়ের প্রচ্ছদে এমন 2-4 টা ছবি থাকলে বই বাজারে ভালো কাটবে 😉। আর এই পুরো বিষয়টাই ফুল অফ কন্টেন্ট সো একটা বইও হতে পারে।এর চেয়ে ভালো বিজনেস আইডিয়া আর হয় না।",0,celebrity
"আমরা অনলাইন ও রাজপথ আছি ,তাকব !!! '""তোমরা যথবার রাজাকার হইবাহ ? আমরা ততোবার মুক্তিযুদ্ধা হইব "" !!! বিজয়ের সূর্য উঠবেই। ইনশা আল্লাহ!!জয় বাংলা!!",0,celebrity
এইমাত্র জানাজা শেষে আমিন বললাম!এখন দেখি পোস্ট!!Nooo😭😭,0,celebrity
স্যার সড়ক দূর্ঘটনায় নিহত বাচ্চাদের নিয়ে কিছু বলতেন!  কোটা অান্দোলন নিয়ে কিছু নাই বললেন,0,celebrity
আমার সেইসবছেলেমেয়েদের জন্যে খুব মায়া হয়যাদের বাবা মায়েরা শুধুমাত্র পরীক্ষায়জিপিএ ফাইভ পাওয়ানোরপ্রতিযোগিতায় নিজেদের সন্তানদেরঠেলে দিয়ে তাদের শৈশবের সব আনন্দকেড়ে নিয়েছেন! তাদের থেকে বড়দুর্ভাগা মনে হয় আর কেউ নেই!,0,celebrity
কমেন্ট পড়তে আসলাম :D,0,celebrity
কমেন্টস পড়তে এসেছি। :) :D,0,celebrity
অভিজিৎ রায়ের হত্যার পর আমি অনেক শঙ্কিত! এই দেশে মুক্তচিন্তা চর্চা করাও মহাপাপ! অভিজিৎ আসছিলেন নিজের দেশে এবং বাঙ্গালির প্রানের মেলা বই মেলাতে ! কিন্তু ফিরলেন লাশ হয়ে !! আমি জাফর স্যারের নিরাপত্তা নিয়ে সঙ্কিত! কারন স্যার ও কিন্তু জঙ্গিদের টার্গেটে আছেন বলে আমি মনে করি। সরকার সহ স্যারের শুভানুধ্যায়ী সকলকে বলব স্যারের প্রতি বিশেষ লক্ষ্য রাখতে। কারন এই ধরনের মানুষদের সংখ্যা বাংলাদেশে এমনিতেই কম। উনাদের নিরাপত্তার খুব বেশি প্রয়োজন। শুভ কামনা স্যারের জন্য।,0,celebrity
"কমেন্ট গুলো পড়তে আসলাম, আর একটু বিনোদন নিলাম, কেউ মাইন্ড খাইয়েন না।",0,celebrity
আমি কমেন্ট পড়তে এবং হা হা গুনতে আসলাম...:p,0,celebrity
একদলীয় শাসন চলছে কিছু বলবেন না৷ বললে দেশ গর্ভবতী হয়ে যাবে আর না বলায় গর্ভপাত৷  কি দরকার কিছু বলার৷  এমনি সব মারা যাক৷,0,celebrity
পোস্ট খেয়ে গাজা লেখবেন না 🙄🙄🙄,0,celebrity
"যারা এখানে চুলকানিমূলক কমেন্ট করে, তারা আদতে রাস্তার নেরিকুত্তা 😡😡",0,celebrity
স্যার একটা কথা বলি আশা করি বিষয়টি নিয়ে  ভাববেন। ক্লাশ কোচিং যেগুলো হয় তাতে মেক্সিমাম স্টুডেন্ট এর অংশগ্রহন থাকে। কোচিং গুলো বন্ধ হলে যেটা হবে ধনীদের ছেলেমেয়েগুলো প্রাইভেট পড়বে। আর অন্যসব ছেলেমেয়েরা বিষয়টি শিখতেই পাড়বে না। কারন শিক্ষাব্যবস্হাটা এতটাই খারাপ যে ক্লাশ নিতে গেলে আপনারা ফাকিবাজি করেন। শিক্ষক ছাড়া আপনি বড় হতে পারবেন বলেন। পারবেন না। আপনাকে কেউ তো শেখাতে হবে এবং পথ দেখাতে হবে। science বিষয় হয় তাহলে তো কথাই নেই। সাহিত্য নই  যে কোন ভাবে লিখব আর হয়ে যাবে। পারলে শিক্ষা ব্যবস্হা সম্পর্কে লিখেন। কারন আপনার লেখা সবার কাছে পৌছাবে আমার লেখা নই। একটা সচেতন জাতি হওয়ার মন্ত্র লিখেন। বিনোদন মূখ্য বিষয় আপনাদের মত শিক্ষকরাই প্রাধন্য দেই। বড় দুঃখ হয় এদেশে বিশ্ববিদ্যালয় গুলো কনসার্ট এর জন্য কোটি কোটি টাকা ব্যয় করে। অথচ গবেষনা খাতে শূন্যার কোঠায়। উচ্চশিক্ষা অর্জনের পরেও তারা ব্যাকার। কেন জানেন গবেষনার অভাব। বিনোদন আর আড্ডাবাজি সমাজটাকে নষ্ট করে দিচ্ছে।সব ভন্ডামী। আপনাদের মত নাস্তিকদের অনুপ্রেরনায় পুলাপাইন নাস্তিক হচ্ছে। নাস্তিকতা নয় ধর্মীয় অনুশাসন মেনে আগামীর সুন্দরের পথে লিখুন। স্যার পারসোনালী আঘাত করার জন্য দুঃখিত।,0,celebrity
"আমাদের জন্য দুঃখ জনক আপনার মতো কুত্তার বাচ্চা শিক্ষক পাইলাম..!আপনে শুধু আওমিলীগ এর ইশতেহারের যুদ্ব্যাপরাধী বিচার সম্পর্ন করার বাহবাদিলেন!অথচ এই শাসনআমলে হাজার ও নিরিহ মানুষ গুম খুনের স্বিকার হয়েছে তার কোন প্রতিবাদ আপনার স্ট্যাটাস এ আসেনাই।এমন কি ৫৭ জন সেনা হত্যা সহ কেন্টরমেন্ট এ তনু হত্যা দ্রব্যমূল্য বৃদ্দি ব্যাং ডাকাতি শেয়ার বাজার দস,এভাবে অসংখ্য মানুষের জিবন নিরবিঘ্নে তার কোন প্রতিবাদ করলেন না!you like a dog",0,celebrity
"ফেসবুকে ফার্স্ট টাইম একটা জিনিসের অভাব বোধ করতেছি। ""বমি রিয়েক্ট"" -_-",0,celebrity
"স্যার, আপনার কমেন্ট বক্সে পোলাপান হরহর করে বমি করছে। বমি জিনিসটার পারষ্পরিক আবেশের মত কাজ করে। কি আর করার,,,",0,celebrity
যেখানে একটা সাদাসিধে মানুষ ও বুঝতে পারে দেশে কি হচ্ছে সেখানে আপনি এতটা অবুঝ শিশুর মত কিভাবে মাঝপক্ষ অবলম্বন করেন???  হ্যা সত্যিই আমরা জানতে চাই  আপনি যেহেতু বুঝতে পারতেছেন বুকের মধ্যে ধক করে উঠেছে ।  সেই ধক করে উঠার কারনটাও আপনি অবশ্যই জানেন।  একটা ব্যাপার হল বোবার কখনো কোন শত্রু নেই আর সাহসীদের মৃত্যু হলে একবারই হয় ।  এইভাবে বারবার বুকে ধক ধক করে নাহ ।,0,celebrity
বিএনপি জামায়াত না টেনে নিরপেক্ষ দৃষ্টিভঙ্গি নিয়ে কথা বলতে শিখ। তাহলে দেশ ও জনতার মঙ্গল হবে।এভাবে একতরফা কথা বলে নির্বুদ্ধিতার পরিচয় দেসনে।,0,celebrity
"স্যার সিলেটে বাতাবী লেবুর চাষ কেমন হয়? একটু যদি বলতেন দয়া করে..😞  অনেকক্ষণ বিটিভি দেখলাম কিন্তু ওরা দিনাজপুরের লেবুর খবর দিচ্ছে, সিলেটের বাতাবী লেবু চাষের খবর জানা খুব দরকার।",0,celebrity
"ড্রাইভার কন্ডাক্টর হেলপার আর মুহাম্মদ জাফর ইকবাল ভূমিষ্ট হওয়ার সময় একই মস্তিষ্ক নিয়ে জন্মায়|এরপর তাদের মধ্যে কেউ মুহাম্মদ জাফর ইকবাল হয়|কেউ হয় ড্রাইভার কন্ডাক্টর হেলপার|ভাগ্যের কারণে হোক,কিংবা সুযোগের অভাবের কারণে হোক দুই পক্ষের ন্যায়''ন্যায়' নামক অনুভূতির ভিন্ন ভিন্ন পারসেপশন তৈরি হয়|একপক্ষ ঘুম থেকে উঠে ঘুমাতে যাওয়ার আগ পর্যন্ত সম্মান ,অর্থ,সামাজিক অবস্থান,জ্ঞান এর প্রাচুর্যে থাকে আর এক শ্রেনী''অনিশ্চয়তা 'নামক ব্যাধি সাথে নিয়ে বেচে থাকে| সিলেট থেকে ঢাকা রওয়ানা হয়ে উভয় পক্ষই যদি সোজা যেতেই থাকতো ,কোন বাহ্যিক বল দ্বারা প্রভাবিত না হতো তাহলে দুনিয়া বিশ পাক ঘুরে এসে সমীকরণ দাড়াতো, মুহাম্মদ  জাফর ইকবাল=ড্রাইভার/হেলপার/কন্ডাক্টর",0,celebrity
আমি ডাঃজাফর সাহেবের পক্ষ হয়ে উপরের সকল কমেন্ট এর বিরুদ্ধে তীব্র নিন্দা জানাচ্ছি,0,celebrity
স্যার আপনি কত নম্বর সেক্টরে মুক্তিযুদ্ধ করেছেন? আপনি বর্তমান বাংলাদেশের সবচাইতে ইম্পরট্যান্ট মুক্তিযোদ্ধা।  আপনাকে নিয়ে সামনের বিসিএস এ প্রশ্ন আসতে পারে।  কিন্তু স্যার আপনি কত নম্বর সেক্টরের মুক্তিযোদ্ধা ছিলেন সেই ডাটা কোথাও পাচ্ছিনা স্যার। দয়াকরে যদি একটু বলে দিতেন স্যার।,0,celebrity
আপনি জনগনের পক্ষে নয়। আপনে পদ লেহন কারী।,0,celebrity
"হাফ লিটার নাকি কান্নায়, একমুঠো আবেগ আর এক চিমটি ইমোশন একসাথে গুলে দিন - ব্যাস হয়ে গেলো ঝটপট যৌক্তিক পোস্ট!",0,celebrity
"রাগ তোর উপরে নয় রে শাউয়ার পুত, রাগ হচ্ছে সরকারের উপর। সরকার কেনো সে সময় তোর বাপ কে রাজা বেলুন আর তোর মা কে সুখী বড়ি ফ্রীতে দেয়নি।",0,celebrity
গায়েবানা জানাজাটা পড়া আর হলোনা 😞😞,0,celebrity
"লেখাটা পড়ে খুব হতাশ হলাম স্যার। ভেবেছিলাম আপনার লেখাতে ছাত্রদের জন্য উৎসাহ থাকবে, তাদের কাজের প্রশংসা পয়েন্ট করে লিখবেন। এবং তাদেরকে বাধাদান কারীদেরও নিন্দা করে কিছু বলবেন। যেমন এই কচি বাচ্চারা পড়ালেখা ছেড়ে রাজপথে নামলো। পুলিশ তাদের পিটালো...।  ছাত্ররা এই পাঁচ দিনে অনেক কিছু শিখিয়েছে। মন্ত্রী, মেয়র, ডিআইজি এমনকি বিজিবির গাড়ি থামিয়েও লাইসেন্স চেক করেছে। ৪৭ বছর পর আমরা প্রথম দেখলাম ইমার্জেন্সী লেন। যেখান দিয়ে এমবুলেন্স গেলো।  তাঁরা হাতে ধরিয়ে অনেক কিছু শিখালো। ক্ষোভে গাড়ি ভাংলেও রাস্তাটা তারাই পরিস্কার করলো।   আপনার লেখায় আশা করেছিলাম তাদের এসব প্রশংসা করে সাহস দিবেন যেন ভবিষতে অন্যায় দেখলে এভাবেই ঝাপিয়ে পড়ে। সে সাথে শান্ত হতে বলবেন যেহেতু সরকার সব দাবী মেনে নিয়েছে বলে আশ্বাস দিয়েছেন।   আপনার লেখায় এসব না পেয়ে মর্মাহত হলাম।",0,celebrity
উদ্দেশ্যটা ভালোই...কিন্তু দেশে চোর বাটপারের তো অভাব নাই...আদৌ কি তা বাস্তবায়ন হবে..!    আর বাস্তবায়ন হলেও প্রশ্ন ফাস হবে না...তার গ্যারান্টি  কে দিবে...?,0,celebrity
স্যার ওপারেও কি ওয়াইফাই আছে!!😱 মৃত্যুর পরেও স্ট্যাটাস দিচ্ছেন! নিশ্চই বেচে থাকতে কোনো মহৎকর্ম করেছিলেন এজন্যই সৃষ্টিকর্তা আপনাকে মোবাইল সাপ্লাই করেছেন😍😍,0,celebrity
"আওয়ামী লীগের আমলেই প্রশ্ন ফাঁস ভাইরল হইলো, মানে গণহারে প্রশ্ন আউট হওয়া শুরু হইলো।  তারা ১০ বছর মুলা চাষ করছে?? এখন ইস্তিহারে প্রশ্ন ফাঁস ঠেকাবে এই অংগীকার করতে গায়ে লাগে নাহ??",0,celebrity
"আপনার পোস্টের কমেন্ট পড়ি আর কাঁদি! ভেবে অবাক হই যে, একজন বীরশ্রেষ্ঠ, মুক্তিযোদ্ধা জাফর ইকবাল আমাদের দেশে কতোটা প্রয়োজন! অথচ পোলাপানের এসব কি কমেন্ট!? 😞 মুক্তিযুদ্ধে সামনের সারি থেকে নেতৃত্ব দেওয়াই কি আপনার একমাত্র অপরাধ? এই দেশ বিরোধী চক্র আপনার সব পোস্ট নিয়েই মজা করে।এসবে কান দিবেন না  স্যার! কৃতজ্ঞতা বীরশ্রেষ্ঠ জাফর ইকবাল! আপনি আমাদের দেশে আছেন বলে আমরা গর্বিত।  আমি আপনার পোস্টের সাথে একমত!",0,celebrity
"আপনার লেখায় কিছু পাব এই আশায় পড়া শুরু করলাম,,এতোদিন পরে এটা কি লিখছেন,?আপনারও তো স্বপ্ন ছিল নিরাপদ সড়ক নিয়ে। দেখেন স্টুডেন্টরা ২-৩ দিনে রাস্তার পরিবেশ চেঞ্জ কটে দিয়েছে,,এখনো আপনি চুপ থাকবেন?",0,celebrity
"এখন তো দেখি এইটা আপনার পুরনো গুণ,অবস্থা খারাপ দেখলেই আপনি পালান,আর পরে এসে লেকচার দেন।একজন প্রকৃত দেশপ্রেমিকের  দেশের সচেয়ে বেশি প্রয়োজন দেশের দূরাবস্থায়।",0,celebrity
"আমাদের প্রাতিষ্টানিক শিক্ষার  যে বেহাল দশা, তাতে  সমন্বিত  পরীক্ষা কোনো উপকারে আসবে না, বরং সেটা শিক্ষার্থীদের জন্য আরো বড় বিপদ ডেকে আনবে,,, সৃজনশীল পদ্ধতির নামে যে ভন্ডামি শুরু হয়েছে আগে সেটা বন্ধ করে এর সঠিক প্রয়োগ নিশ্চত করতে হবে,,প্রাতিষ্টানিক শিক্ষার মান বাড়াতে হবে,,,",0,celebrity
আপনাকে কিভাবে বিশেষনে বিশোষিত করব বাক্য পাচ্ছি না।,0,celebrity
বিপদে পরলে আল্লাহ কে ডাকে। আর না হলে চিনে না।,0,celebrity
ঐ মুরগী চুর স্যারকে ধর,0,celebrity
জাফর স্যার পোস্ট করলেই আমার ইদ ইদ লাগে।সবাইকে দুই দলে বিভক্ত করে দিয়ে উনি মাতালের মতো ঘুমান।সবাই জামাত বেঁধে উনার কমেন্ট বক্সে উৎসবে মাতে।  ৯০% পোস্ট না পড়েই গালি দেয়।এটা উনার অর্জন না খ্যাতি বুঝিনা।,0,celebrity
দারুণ স্যার।,0,celebrity
"দুর্বল চিত্তের মানুষটাকে তোমরা এভাবে বকাঝকা করছো? ছিঃ ছিঃ ছিঃ ! 'কোথায় আছি আমরা, কি অবস্থায় আছি আমরা'",0,celebrity
কেউ নিজেকে কেন রাজাকার বলবে? নিশ্চয় এর কোনো কারণ আছে। আগে সেটা জানুন। সবকিছু মুক্তিযুদ্ধের চোখ দিয়ে বিচার করেণ ভালো কথা কিন্তু অন্ধ হয়ে যায়েন না।,0,celebrity
"আমার অভিযাত্রী তরুণ সেনা,ওরা মানে না অনিয়ম, নতুন দিনের যোদ্ধাদল,শুধু ওরাই ব্যতিক্রম। ওরা বিদ্রোহী,ওরা শান্ত,সমাজ ওদের বোঝেনি,উপহাসের অট্টহাঁসি,ওরা হয়েছে হাঁসির পাত্র। ওরা থামেনি,হয়নি খান্ত, রাজত্তের নিশান তুলেছে,ওরা খেলেছে, ওরা জিতেছে,ওরা যোদ্ধা,ওরা হটায় ভয়, প্রহসন থেমে যায়,ওরা বিজেতা ওরা তো বিজয় ছিনিয়ে নেয় একদিন আমি নেই,থেকে যাবে আমার দর্শন,আমি জানি ওরা বাঁইবে তরী,ওরাই ধরবে হাল,আমি জানি ওরা পারবে,ওদের ভিতর শক্তি অপার লাল সবুজ হবে কলঙ্ক মুক্ত™",0,celebrity
এইদিকে আসেন! সবাই দেখে যান! গায়েবানা জানাজা হওয়া ব্যক্তি কিভাবে কবর (গর্ত) থেকে বেরিয়ে আসে.....,0,celebrity
এত বড় গরুর রচনা লিখার দরকার কি ছিলো?বললেই হতো AL  এর ইশতেহার I'm GPA 5 এর মত।  ভোট ফর নৌকা... 😂,0,celebrity
সার নামাজ পড়েন জীবন গড়েন৷ বয়স তো আর কম হলো না ৷ সব চুল তো পেকে সাদা ৷,0,celebrity
"আই বার্তা শেয়ার/ লাইক কুইজ প্রতিযোগিতা-২০১৪.  সবাইকে অংশগ্রহন করার জন্য অনুরোধ করা হচ্ছে ।  শুধু মাত্র এই মহান বিজয় দিবস , ডিসেম্বর মাসে চলবে।  তাই আজই আই বার্তার পেজ লিংক আপনার বন্ধুদের শেয়ার করে জিতে নিন বিভিন্ন গিফট্‌ । https://www.facebook.com/ibartanews",0,celebrity
স্যার আপনি জানেন ছেলেটি কেন আমি রাজাকার লিখেছে+?,0,celebrity
নটি অন করে গেলাম।কিছুক্ষণ পর পর এসে কমেন্ট পড়ে যাব। এভাবেই চলতে হবে আগামি কলাম না লিখা পর্জন্ত।আমার বিনোদনের মাধ্যম একমাত্র আপনি স্যার।💜💜,0,celebrity
অতঃপর কিছুদিন পর বলবেন আগে জানলে ভেজাল গাজা খাইতাম না।,0,celebrity
মাতাল হইলেন কবে প্রিয় স্যার ;-),0,celebrity
"আমেরিকার গনতন্ত্র নিয়ে লিখালিখি করার পূবে' সটীক তথ্য জেনে লিখবেন।আমি এই দেশে গত ২৫ বছর থেকে বাসকরতেছি,বাংলাদেশের এবং আমেরিকার  গনতন্ত্র আকাশ পাতাল ভেবদান।",0,celebrity
"স্যার খবর দেখেন না, খবর শুনেন না,   :-)খবর তৈরি করেন,,.👀🔫 #গুজব না কিন্তু... 😷",0,celebrity
"আপনার আশু বোধদয় হোক, এটা সবার চাওয়া। অনেকদিন পর বাস্কের বাহিরে এসে লেখার চেস্টা করেছেন, কিছু সত্য তুলে আনার চেস্টা করেছেন। একটু সাবধানে থাইকেন স্যার।",0,celebrity
"স্যার এসব বাদ দিয়ে একটা মনোনয়নপত্র কিনেন, যা মাল লাগে আমি দিবো🐸🐸",0,celebrity
"কেও ঠেলাঠেলি করিয়েন না, লাইনে দাড়িয়ে সবর করেন। সবাই হর হর ভমি করার সুযোগ পাবেন ইনসাআল্লাহ।",0,celebrity
পোষ্ট উহু মোটেই না শুধুই কমেন্ট পড়তে আসলাম,0,celebrity
মামলা করে কোন লাভ হবে না। সরাসরি বিচার।,0,celebrity
"উনি আবার কিছু কিছু কথা বলেন, যার কারণে উনাকে আবার অনেকে নাস্তিক দাবি করে  তবে আমি উনাকে নাস্তিক মনে করিনা কারণ নাস্তিকরা তো কোন ধর্ম বা ধর্মের মানুষ কে ঘায়েল করে কথা বলেন না  একটু কমেন্ট করলাম আর কি, সকলের কমেন্ট গুলো পড়ে অনেক ভালো লাগলো যে এই সব জাফর ইকবালদেরকে এখন আর মানুষ অন্ধ অনুকরণ করে না",0,celebrity
দালাল,0,celebrity
না ভেবেছিলাম একটা নীতি-ইতি বাচক কমেন্ট করবো... তা আর সম্ভব নয়..  এই লেখকের পাঠক বেশি... চলে যাচ্ছি..,0,celebrity
"গা বাচিয়ে যে পোষ্ট করছেন বুঝা যাচ্ছে, লেখার স্বার্থকতা আসবে না যদি না সব কিছু জেনে শুনে সকল তথ্য না দেখে কথা বলেন। লেখেছেন ই যখন প্রাণ খুলে লেখুন, কলম কে শক্ত জায়গায় দাড় করানোর দায়িত্বটাও আপনার মত লেখকদের..।",0,celebrity
মরা মানুষ জেন্দা হইলেন কেমনে 😂,0,celebrity
"নিচের লেখাটি পড়ুন, তারপর নিজেকে সেখানে দাড় করান, ভাবুন নিজের বাবার সাথে এটা হলে আপনি কি করতেন যখন দেখতেন স্বাধীনতার এত বছর পর কেউ বুকে রাজাকার লেখা নিয়ে ঘুরছে। পুরো দুনিয়া দিয়ে দিয়েও যদি কেউ অলংকার-বালাংকার যেভাবেই বোঝাই না কেন  রাজাকার শব্দ কানে কুলাঙ্গারের মত বাজবেই । যদি না বাজে তাহলে সে নিজেই সে কুলাঙ্গারদের তালিকার প্রথম সারিতে থাকবে !!!   # মা কে বিশ্বাস করানোর জন্য সত্যি সত্যি আমি আমার বাবার কবরটা খুঁড়েছিলাম। আমার বাবা পা দুটি ভাজ করে সেখানে শুয়েছিলেন। দশ মাসে তার হাড়গুলি ছাড়া আর কিছুই ছিল নআআ, শুধু তার দুই পায়ে ছিল দুটি মোজা, নাইলনের মোজা বলে এতদিনেও কিছু হয় নি। যখন এই মোজাগুলি পরছিলেন আমি সামনে ছিলাম, এতদিন পরে সেই মোজা পায়ে আমার বাবা কবরের মাঝে শুয়ে আছেন, এই পুরো ব্যপারটাতে কেমন জানি একটা ভয়াবহ কষ্ট লুকিয়ে আছে। আমি খুটিয়ে খুটিয়ে আমার বাবা কে দেখলাম। অনেক কয়টি গুলি লেগেছিল তার শরীরে, অনেকটা আদর করার মত হাত বুলিয়ে দিলাম সেই গুলির আঘাতে। একটি গুলি লেগেছিল মাথায়, কেমন লাগে মানুষের মাথায় গুলি লাগলে??......... তার শরীরের হাড়গুলি একটা একক্টা করে কফিনে সাজিয়ে তুলে আমার মাকে গিয়ে দ্বিতীয়বার তার মৃত্যুসংবাদ দিলাম। একটা গাছের নিচে হাটুতে মুখ গুজে বসে ছিলেন আমার মা। তিনি তখন প্রথমবার তার মৃত স্বামীর জন্য কাদঁলেন। নির্জন একটা নদীতীরে আমার দুঃখী মাকে কাঁদতে দেখে আমার বুকের ভিতরে কিছু একটা গোলমাল হয়ে গেল। আমি ঋষি দুর্বাসা নই, হলে সেদিন ছারখার হয়ে যেত অর্ধেক পৃথিবী।"" ----মুহাম্মদ জাফর ইকবাল---",0,celebrity
"মদের দোকানে বসে,ধর্ম নিয়ে আলোচনা যেমন হাস্যকর,জাফর ইক-বালের মুখে,মুক্তিযাদ্ধ নিয়ে কথা শুনা অনেকটা সেই রকম হাস্যকর..!  মুখে আঙ্গুল দিয়ে বুমি করতে হয় না জাফর ইক-বালের চেহেরা দেখলেই আমার বমি আসে..!",0,celebrity
হ্যাপী নিউ ইয়ার বত্ব!ভোট কয়টা দিসিলেন?,0,celebrity
"ইনশাল্লাহ্ আপনি সুস্থ হয়ে  উঠুন! আসুন আমাদরে মাঝে, আমারা আপনার অপেক্ষায় আছি। বড় প্রতিকুল সময় দিয়ে যাছ্ছি আমরা।",0,celebrity
"স্যার আপনার রচনাটি পড়ে আপনার অন্তরের গভীরে প্রোথিত ব্যাথার আভাষটুকু বুঝার চেষ্টা করেছি। আসলে প্রতিটি কথার নেগেটিভ একটা রুপ ও থাকে, সকলে সেটা বুঝতে পারেনা কেবল জ্ঞানী আর বিজ্ঞজনরা প্রতিটি ঘটনার তলানীটুকু ও অনুধাবন করার চেষ্টা করে যা আমাদের মতো ব্যক্তি স্বার্থচিন্তার অধিকারীরা বুঝতে পারেনা। আরো অনেক কথা বলার ছিল কিন্তু পথে বসে পথের দাবী আদায় করা যায়না কখনো জ্ঞানের ও পরিচয় দিতে হয়। আপনার দীর্ঘায়ু কামনা করি।",0,celebrity
আমরা চট্রগ্রামে ও শুরু করতে চাই এ আন্দোলন.........,0,celebrity
এই লিখা যখন লিখছেন সরকার কিন্ত তখন তাদের প্রতিরোধ করা শুরু করছে। মাঠ পর্যবেক্ষণ ভালভাবে  না করেই লিখাটা পোষ্ট করা  কি ঠিক হলো স্যার!,0,celebrity
স্যার এতোদিন শুধু ভাবছে কীভাবে এ ঘটনাকে দালালাইজেশন করে পোস্ট করা যায় ।,0,celebrity
"এত গুনিজন থাকতে কি আর কমেন্ট করা যায়!তাই পড়তে আসছি,অনেদিন ভাই প্রাণখুলে হাসিনা তাই হাসছি।",0,celebrity
আমি এখন মদ খাবো আর কমেন্ট পড়বো,0,celebrity
বঙ্গবন্ধু হত্যার পরোক্ষ ভূমিকা কার তা খুজেঁ বের করার জন্য অবসরপ্রাপ্ত বিচারপতিদের নিয়ে কমিশন গঠন করা দরকার।,0,celebrity
এই বুইড়া কই যুদ্ধ করছে?,0,celebrity
"আপনার গায়েবানা জানাজা তো কালকেই পড়ছি আর আজকে জুম্মাবাদ মিলাদও ছিল আর এখন দেখি আপনি বাইচ্যা আছেন!!  কিশোর বয়সে অনেক ভাল ভাল স্মৃতি নিয়ে বড় হইছি আপনার বইগুলো পড়ে,বইগুলো পড়ে আনন্দে দুঃখে কত কানছি,,একবার এক ফ্রেন্ড আপনাকে চিঠি লিখছিল আর আপনি তার রিপ্লাইও দিছিলেন,,সেই চিঠি একবার ছুয়ে দেখার জন্য কত আবেগ,,কত টিফিনে না খেয়ে থাকছি টাকা জমিয়ে আপনার একটা বই কেনার জন্য,,আর এখন মনে হয় আপনার সব বইগুলো নিয়ে তার উপর হড় হড় করে বমি করে দেই,,কিন্তু দেইনি ,যত্ন করে রেখে দিছি আমার ছেলেমেয়ের জন্য,,,আমি যে আনন্দ পাইছি আপনার বই পড়ে ওরাও সেটা পাক।।।",0,celebrity
"জনাবের কথা গুলো বিশ্লেষণ করলে কিছু ভ্রান্ত ধারনা পাওয়া যায়, উনি বলেছেন কোটাবিরোধী আসলে সংস্কারবাদী আমরা, আন্দোলনে জনজীবন বিপত্তি যে প্রসঙ্গ টানলেন শাহবাগের আন্দোলনের সময় কোথায় ছিল তার মানবতা।শ্রদ্ধা করতাম আপনাকে এখন ভাবছি ভুল করেছি।",0,celebrity
কদিন পর আবার সুর না পাল্টালেই হয়।,0,celebrity
আমার মনে হয় পেইজ টা #Hack করা হয়েছে।  😒  চক্রান্তের  শিকার তিনি  😒. কেউ ইচ্ছে করে এই কাজ টা করেছে 😒,0,celebrity
সহমত ভাই,0,celebrity
স্যার সম্ভবত শুধু অর্গাজম বুঝেন......সার্কাজম বুঝেন না 😒😖,0,celebrity
চাটুকারিতা অনেকে আপনার কাছ থেকেই শিখেছে।,0,celebrity
"ক্ষমতাধরদের একের পর এক চামচামী করতে করতে আপনি যেভাবে এদেশের যুবাদের কাছে হিরো থেকে ভিলেনে পরিণত হলেন, আমি অনেক বছর আগেই আপনার গায়েবানা জানাজা পড়ে ফেলেছি। আপনার কবরের উপর একটি শিমুল গাছও লাগিয়েছি। ফুল ফোঁটার অপেক্ষায়।  তাই বলছি, হড়হড় করে বারবার এভাবে বমি করে আর পরিবেশ দূষন করবেন না। এবার তফাতে যান।",0,celebrity
সুবিধাবাদী,0,celebrity
প্রিয় মানুষ ♥,0,celebrity
স্যার সিলেটে লাউ চাষ কেমন হয়???,0,celebrity
"৪০ বছরের কথা ভুলতে পারনের না""!! নিরাপদ সড়ক দাবী নিয়া কোন পোস্ট দেখলাম না।",0,celebrity
সবাই সাবধান স্যারের কিন্তু গায়েবী জানাজা হয়ে  গেছে এটা নিশ্চয় স্যারের ফেলে যাওয়া ড্রোন গুলোর কাজ।?🖕🖕👮,0,celebrity
"১) নবম অধ্যায়ে বলা আছে ( ৯.২.১ ) ""রংধনু তৈরি হয় পানি কণার ভেতরে পুর্ণ অভ্যন্তরীণ প্রতিফলন এর ফলে ""। তথ্যটি সংশোধন করা উচিত। পানির কণার ভিতরে পুর্ণ অভ্যন্তরীণ প্রতিফলন জ্যামিতিক ভাবেই অসম্ভব। রংধনু এর মুল কারন পানির কনার ভিতরে আংশিক প্রতিফলন এবং বিচ্ছুরণ।  এই link টি দেখার অনুরোধ রইল। http://en.wikipedia.org/wiki/Rainbow wikipedia->Rainbow->Explanation->3rd paragraph এ দেখলেই বিভ্রান্তি দূর হওয়ার কথা। ২) S M Darus Salam ভাইয়ের সাথে একমত। গানিতিক পুর্বজ্ঞান খুব জরুরী।এই বিষয়ে একটি আলাদা অধ্যায় (প্রাঞ্জল ভাষায়, প্রচুর উদাহরণসহ) থাকা উচিত। ৩) একবারে ৩০০ পৃষ্ঠার বই কতজন কিনতে চাইবে/পারবে সেইটাও দেখার বিষয়। তবে সেটি গৌণ ব্যাপার।",0,celebrity
হা হা হা রিয়েক্ট  দিছি। এটা একটা ফানি পেইজ। মন খারাপ থাকলে এই পেজের যেকোনো পোস্টের মন্তব্যের ঘরে চলে যান। বিনোদন অপেক্ষা করে।।।।,0,celebrity
মুক্তিযুদ্ধের সময় তুই কোথায় ছিলি মাদারচোদ??,0,celebrity
বাহ্,0,celebrity
যা মনে করছিলাম তাই.......পরের বছর এতা নিয়ে বই বের করেন কিন্তু??,0,celebrity
মোনাফেকি ছাড়ুন,0,celebrity
চেতনার নস্ট ডুগডুগি বাজাতে বাজাতে প্রজন্মকে কি পরিমান হিপনোটাইজ করা হয়েছে যে প্রজন্ম উল্টো জাফর ইকবাল কেই কমেন্ট প্রত্যাঘাতের উন্মাদনায় রীতিমতো আস্তাকুঁড়ে ছুড়ে ফেলে।,0,celebrity
"আমরা আপনাকে হারাতে চাই না স্যার ❤ জঙ্গিবাদ নিপাত যাক, দ্রুত সুস্থ হয়ে উঠুন এটাই প্রার্থনা করি 😍",0,celebrity
কমেন্টস দেখে তো আমি শিহরিত হয়ে গেলাম 😹😹🐸,0,celebrity
"অসাদারন,,বাবা,,,",0,celebrity
ইবলিসদের আবার অভিশাপের ভয় কি ?,0,celebrity
"স্যার, আপনি ভুল তথ্য পেয়েছেন, আপনার দৃষ্টিভঙ্গিতেও ভুল ছিল।স্যার আপনিই পূর্বের একটি পোস্টে বলেছিলেন না কে কোন দৃষ্টিভঙ্গি থেকে দেখছে তার উপর নির্ভর করে অনেক কিছু।আপনি আপনার এই পোস্টটি করেছেন ৭১এ অবস্থান করে।ওই যে আপনি বললনে না যে কিছু নিউজ পোর্টাল আর একটা ইংরেজি দৈনিকে আপনি সীমাবদ্ধ, আপনার এই বিষয়ে জ্ঞানটাও এরই মতো সীমাবদ্ধ। স্যার এটা ৭১না এটা ১৮।১৮তে কি হচ্ছে তা আপনি ওইটুকুর মধ্যে সীমাবদ্ধ থেকে বুজতে পারবেন না। স্যার, জানি আপনি একটা বড় আঘাত প্রাপ্ত, যদি আপনার মস্তিষ্কে, মনে আঘাত লেগে থাকে প্লিজ স্যার চিকিৎসা হোন। আশা করি জেনে, বুঝে পরবর্তীতে আপনার এই বক্তব্যটির জন্য দুঃখ প্রকাশ করবেন।",0,celebrity
৪ সন্তানের জননীকে যেভাবে ১৪/১৫ আপনার সরকারের লোক মিলে গণধর্ষণ করলো এসব খবর কি রাখেন? নাকি শুধু উন্নয়ন উন্নয়ন আর উন্নয়ন দেখেন গর্ত বাবা।,0,celebrity
একদল ফাজিল আছে এখনো বেহায়ার মত মিথ্যাচার করেই যাচ্ছে । মতিয়া চৌধুরী নাকি তার বক্তব্যে আন্দোলন কারীদের রাজাকার এর বাচ্চা বলেছে । পুরো ১২ মিনিটের বক্তব্যে কোথায় আন্দোলনকারীদের রাজাকারের বাচ্চা বলেছে সবাইকে একটা বরাহ শাবকও দেখাতে পারছে না । ভিডিও তো ইউটিউবেই আছে । ভিডিও আপলোড করে দেখাক কত মিনিট কত সেকেন্ডে সবাইকে রাজাকারের বাচ্চা বলা হয়েছে । পারবে না ইভেন ভিডিও আপ্লোডও করবে না  । কারন পরিষ্কার এটা একটা গুজব । গুজব ছড়িয়ে মানুষকে উত্তেজিত করে আন্দোলন এই বাংলাদেশে একটা গোষ্টীই করে । তার না ম নেয়ার কি দরকার ? পাঠক এর মনে মনেই নামটা উচ্চারিত হয়ে গিয়েছে ! :P,0,celebrity
আপনার মত বেহায়াতো বাপের জন্মেও দেখিনি।।,0,celebrity
"আপনাদের মত পিশাচ মতলববাজ হারামজাদা ( মুরগি কবির , মুন্তাসির মামুন , খুশি )যতদিন বাংলার বুকে বেচে থাকবে ততদিন দেশ অসাম্প্রদায়ীক সুন্দর ও শান্তিময় হওয়া আদেও সম্ভব না । বাংলার বুকে যত অশান্তি অরাজকতা তা আপনাদেরমত গিরগিটদের মাধ্যেই হয়ে থাকে ॥",0,celebrity
ইসলামী আন্দোলন বাংলাদেশ নামে একটা দল হাতপাখা প্রতীকে প্রায় সবকটি আসনে নির্বাচনে একক ভাবে প্রতিদ্বন্দ্বিতা করছে। যারা ইতিমধ্যে নিজেদেরকে দেশের তৃতীয় রাজনৈতিক শক্তি হিসেবে প্রমাণ করেছে।  স্যার কি বিষয়টা এড়িয়ে গেছেন? একচোখা দৃষ্টিভঙ্গি যাদের তারা সমাজের বাস্তবতা দেখতে পায় না।  এরা অনেকাংশেই অজ্ঞ থেকে যায়।,0,celebrity
"যারা মন্তব্য করছেন বানান ঠিক রাখবেন। উত্তেজিত অবস্থায় দ্রুত মন্তব্য করায় বানান ভুল করবেন না। আমরা যারা মন্তব্য পড়ি, আমাদের পড়তে বেশ অসুবিধা হয়। জনস্বার্থেঃ কমেন্ট রিডার অ্যাসোসিয়েশন অফ বাংলাদেশ🐸",0,celebrity
আমি খুবই গর্বিত কারণ গত ২০শে ফেব্রুয়ারি আমি বই মেলায় গিয়েছিলাম এবং সৌভাগ্যক্রমে আপনার সাক্ষাত পেয়েছিলাম এবং লাইন ধরে অপেক্ষা করে আপনার অটোগ্রাফ পেয়েছি। এই অভিজ্ঞতা আমি কখনোই ভুলব না......,0,celebrity
০৪-০৮-২০১৮... স্যার এখন আপনি কই...??? কোথায় আপনার মোটিভেশন...??? কোথায় আপনার যুক্তি...???,0,celebrity
আপনি হয়তো এই বাক্যে বিশ্বাসী নন...  একবার রাজাকার চিরদিনের রাজাকার... একবারের মুক্তিযোদ্ধা চিরকালে মুক্তিযোদ্ধা নয়... আজকে আমি চরমভাবে মিস করছি হূমায়ুন আজাদ স্যারকে... মিস হিম আ লট...  আসলেই মনে হয় সব নষ্টদের দখলে চলে যাচ্ছে... - রাসেল রহমান,0,celebrity
আমি খালি শুনমু,0,celebrity
স্যার ঘটনা টা নিয়ে আপনার লিখা  প্রত্যাশা করি নাই!আপনার প্রতি ভালোবাসা টা হারিয়ে যাচ্ছে কেন !! 😢😢😢,0,celebrity
রক্তহীম করা পোস্ট।।,0,celebrity
বুইড়া খাটাস,0,celebrity
আসেন সুশৃঙ্খল ভাবে কমেন্ট পড়ি! নিজে মজা নিন আর অন্যকেও সুযোগ দিন।,0,celebrity
"ছোটখাটো একটা নির্বাচনী প্রচার হয়ে গেলো। যাই হোক, আমি বলবো দুর্নিতি মুক্ত বাংলাদেশ গড়ার অঙ্গীকার ১ নম্বরে হওয়া উচিৎ, যা আপনার চয়েজএ নাই। কারন হিসেবে বলবো বাংলাদেশে উন্নয়নের উন্নতির চেয়ে দুর্নিতিই বেশি।",0,celebrity
সবাই রাজাকার।।।।,0,celebrity
"কে তুমি বৎস, ধরিয়া মৎস, বেচিয়া গঞ্জে, অকুল ও কুঞ্জে, না খাইয়া তাজা, কেনো ভক্ষন করিয়াছো মেয়াদ উত্তীর্ণ গাজা 😂😂",0,celebrity
পোলাপান ইভেন্ট দিয়ে  গায়েবী জানাজা পড়ার পর সারের চেতনা ফিরছে😂😂😂,0,celebrity
কমেন্ট গুলার কোনো  রিপ্লাই দেয় না কেনো??? নাকি আবার গিয়াছে গান্জার দরবারে???,0,celebrity
"হুদাই আবোল তাবল পেচাল না পেরে বলেন আমার বুবুজানকে ভোটদিন চুষে খাওয়ার সুযোগ দিন😂😂। আর যদি নিজেই নির্বাচনে দারাতে চান তাহলে দারা যান আমরা আপনার নির্বাচন করে দেবোনে তাও দালালি করার দরকার নাই😂  আমার ভাই আপনার চাচা, জাফর আংকেল জাফর আংকেল😂😂",0,celebrity
"ধন্যবাদ স্যার এই পোষ্টটি করার সাহসের জন্য। নিকটভবিষ্যতে হয়ত ""ইমরান সরকার"" এর মত মুচলেকা দিয়ে আপনার মুখও বন্ধ করা হবে।",0,celebrity
আমি বিদেশ চলে যাবো,0,celebrity
২০০৪ সালে একুশে পদক টা নেওয়ার সময় এই ফিল্টার টা ছিলো কই? ভন্ড দেখছি কিন্তু আপনার মত ভন্ড দেখি নাই অবশ্য আপনার নাম টাও তো জাফর!!,0,celebrity
"আমাদের সোনার বাংলা এখনও মরে নি, কিন্তু দলকানারা বুদ্ধিজীবীরা যেভাবে টুটি চেপে ধরছে তাতে মরতে খুব বেশি সময় লাগবে না।",0,celebrity
স্যার এবার আন্নে মুতি গিয়া হুতি থাকেন...,0,celebrity
আমার মাথা,0,celebrity
"যারা অশ্লীল ভাষায় স্যারকে গালি দিয়েছেন,তারা আগে ভাষা শিখুন।",0,celebrity
"বহুনির্বাচনী প্রশ্নে সেট কোড এসেছে একটা কিন্তু খাতায় পূরণ করেছে আর একটা , আবার উত্তর দাগিয়েছে যেটা সেট কোড এসেছে সেটার , এতে করে কি রেজাল্ট ফেল আসবে , কেউ কি নিশ্চিতভাবে জানাতে পারবেন ? ? ?",0,celebrity
অনেক দিন তো জ্বালাইয়া খাইছোস.. এবার একটু মুক্তি দে দেশটাকে. তোর ছোটভাই চলে গেছে তুই যাস না কেন? প্লিজ এবার মর.,0,celebrity
"wow   :-)                         it's definitely amazing picture... thanks *Naim to draw the picture... ""Happy Birthday"" toooo *Zafar sir...",0,celebrity
সরকারের বিরুদ্ধে যারা লেখালিখি করে তারা বীরপুরুষ।   কিছু লোক গর্ত থেকে এসে অক অক করে বমি করে বলে কি হচ্ছে এসব।এই ছুপা গুলা দেশের জন্য ভয়ানক।,0,celebrity
"এই দেশ জনগনের দেশ না, এটি পুরো কিছু হিংস্র পশুর দেশ হয়ে যাচ্ছে, হিংস্র কিছু হায়না এই দেশকে ধংশের মুখে ফেলে দেশবাশিকে  বাশঁ  দিয়ে রাখছে।",0,celebrity
"এখানে পাকিস্তানী জাতীয় পশু ঢুকলো কিভাবে? এখানে কাঁঠাল পাতা নেই। তোদের জন্য বাঁশের কেল্লা, নয়া দিগন্ত, আমার দেশ প্রচুর কাঁঠাল পাতা মজুূদ রেখেছে। ওখানে যা।",0,celebrity
"অপস্ শেষ মেষ তাহারে পাইলাম,আমরা বেকুব জাতি তাকে পাইলাম! দেখলাম,খাইলাম,গিলিলাম অবশেষে হজম করিয়া ফেলিলাম! অবশেষে কমেন্টগুলা পড়িতে পড়িতে বদহজমে প্রায়!  তবে ষ্যার আপনে যদি একটু সময় পান,দয়া করে কমেন্টগুলা পড়ে মনে কথাগুলা জানিয়েন! তবে বমির কথা আর বইলেন না যেন,কারন আপনে একা,নিত্যান্তই একা আর পাবলিক বহুত!  মাথায় উঠাইতে সময় নিবো না,তবে সেখান থেকে নামিয়ে ছুড়ে ফ্লাইতেও একটুও ভাববো না!",0,celebrity
লুল 😂😂😂😂,0,celebrity
নোয়াখালী বিভাগ চাই স্যার 😃😃😆😉😎,0,celebrity
"তুমি আসছো আওয়ামীদের চামচামী করতে,,,, গত ১০ বছরে ওই লুকিয়ে থাকা গর্তের ই উন্নতি হয়েছে,মানে লুকিয়ে থাকতে তোমার সুবিধে হবে, শালাষাঁড় কোনখানের",0,celebrity
আরে 😒😒😒 এই উপন্যস এর নাম কি কেউ বলবেন??,0,celebrity
গণধর্ষন শুনলে উনার চেতনাদন্ড দাঁড়িয়ে যায়🤣🤣🤣,0,celebrity
yep sir u r right,0,celebrity
"স্যার আমরা আপনার কাছে ক্ষমাপ্রার্থী, এ দেশের জন্য আপনার এত বড় ত্যাগের বিনিময়ে আমরা এ দেশের মানুষ আপনাকে কিছুই দিতে পারলাম না লাঞ্ছনা ছাড়া... :'(",0,celebrity
মুক্তিযুদ্ধের বাংলাদেশ চাই। রাজাকারের বাংলা চাই না।,0,celebrity
শ্রদ্ধেয়  ভাইয়েরা !!! আমারে একটু জায়গা দিয়েন.#এনা_হর_হর_করে_বমি করতাম। কী আর কমু উনার মতো তো আর পল্টিবাজ কথার কারিগর হইবার পামু না তাই এটুকুই কইলাম।  ধন্যবাদ  ভাইয়েরা একটু জায়গা দেয়ার জন্য ।।।,0,celebrity
দলকানা চাটুকার বুদ্ধি বেশ্যা হলে এমনই হয়৷,0,celebrity
বাংলাদেশের লোক জন সত‍্যিই অসুস্থ। ....,0,celebrity
"প্রযুক্তি কে ব্যবহার করব কিন্তু প্রযুক্তি যেনো আমাকে  ব্যবহার না করে।দারুন লেগেছে।এক ,দুই,তিন নাম্বার পিলারদের পক্ষ থেকে বলছি চার নাম্বার দেখতে চাই।",0,celebrity
"এই সরকারের আমলে আপনার মত অভিজ্ঞ চাটারদের এরকম পরিস্থিতি আশা করি হবেনা,, তবেঁ পরিবর্তী সময়ে চাটুকারিতার ফল ভোগ করার জন্য প্রস্তুতি নিয়ে রাখবেন।।",0,celebrity
Your mother always inspires us sir.,0,celebrity
আমি বর্তমানের এমন একজন রাজনীতিবিদের নাম জানতে চায় যিনি কিনা দেশপ্রেমিক !!!!!!!!!!,0,celebrity
সহমত ভাই।লেখাটা জোস ছিলো।২য় আর ৩য় নাম্বার প্যারাটা আরেকটু গুছিয়ে লিখলে ভালো হইতো।লাষ্ট প্যারাটা অসম্ভব সুন্দর হয়েছে।🐸,0,celebrity
"sir, আপনার এই কথাগুলোর মূল্য সরকার দেবেনা। এই দেশে এমন কোন সেক্টর নেই যেখানে ভেজাল নাই। আর ভেজাল ছারা রাজনৈতিক ব্যাক্তি হওয়া যায়না।",0,celebrity
"বুদ্ধিজীবীরা এখন বিভক্ত তিন গোত্রে। ভন্ড, ভন্ডতর, ভন্ডতম। -হুমায়ূন আজাদ",0,celebrity
স্রোতের সাথে সাথে চলা জামাত শিবিরের মত খাচিয়ত আমাদের জ ইকবাল সাহেবের। পরিস্তিতির অনুকূলে কলম ধরতে আপনাদের অনেক সাহস। আর প্রতিকুলে আপনাদের সাহস বার্ণ ইউনিটে,0,celebrity
"বমি খা,মানুষ হ😁",0,celebrity
কমেন্টস পড়তে আসিলাম এই মৃত ব্যাক্তির পেজে🐸🐸,0,celebrity
পপকর্ণ নিয়া কমেন্ট পড়তে বসলাম। বউকে হালকা ছোলা আর পেয়াজু ভাজতেও বলে দিসি।,0,celebrity
"আহ এই লেখা পড়ে আজ চোখ খুলে গেলো স্যার। আগেও খোলা ছিল, মাঝখানে এই দুস্ট কোটা আন্দোলনকারীরা, সড়ক আন্দোলনকারীরা একটু অন্ধ করে দিছিলো।। আজ আবার চোখ ফিরে পেলাম স্যার।।",0,celebrity
"সামান্য ""আমি রাজাকার"" লেখা থাকায় মুখ ফিরিয়ে নিলেন। আর দেশবাসী  ও বুঝতে পারল একজন মানুষ কে। কথায় আছে, বিপদে পরলে মানুসের আসল রুপ চেনা জায়।",0,celebrity
শুয়োরটা এখানে???,0,celebrity
আমার দোয়া মহান আল্লাহ্ প্রায়ই কবুল করে থাকেন কারন আমি আল্লাহ্ ও আল্লাহর রাসুল (স:) কে বিশ্বাস করি.. এই বিশ্বাস করা হচ্ছে ঈমান . যার ঈমান আছে তার কবুল হয় আর যার নাই তার কিয়ামতের দিনেও হবেনা .,0,celebrity
"স্যার অবশেষে গর্ত থেকে বের হলেন,",0,celebrity
অবশ্যপালনীয়,0,celebrity
"একটা কাম করেন, আমনে একটা সার্চ ইঞ্জিন বানায়া ফেলেন। নাম দিবেন #টুনটুনাটুনটুন",0,celebrity
আমি নিজেও একজন শিক্ষক। কিন্তু কি বলব ভেবেই পাইনা। আমরা পুরো একটা জাতিকে আস্তে আস্তে ধ্বংস করে দিচ্ছি!,0,celebrity
স্যার! আপনি বেঁচে আছেন!?,0,celebrity
জ্বি আমি। একটা প্রশ্ন করতে চেয়েছিলাম।  আবার বৃষ্টিতে বসে কেঁদে দিবেননা তো??,0,celebrity
"প্রতিক্রিয়া পড়বেন কেমন করে!! আপনি যে কতবড় লুইচ্ছা, কত বড় নাস্তিক এসব কি আর শুনতে ভাল লাগে!!",0,celebrity
আমি সরকারি চাকরির আশা ঐ দিনই বাদ দিয়েছি যে দিন পুলিশের SI পদে চাকরির জন্য     20 LAK টাকা ঘুষ দিতে হবে যদি Training এ ও exam এ successfully হই। যাক আমরা দু  বন্ধু রাজি হই। কিন্তু টাকাগুলোও কাকে দেব। সে যদি টাকাগুলোও মেরে দেয়। আর হলো না সরকারি চাকরি। বাকিটা ইতিহাস। Masters এ 1st class পেয়েও 3টা 1st class নিয়ে এখন private একটি BANK এ 5 বছর যাবত PEON এর JOB করিতেছেন । জাতীর কছে জানতে চাই আমি কি যোগ্যতার ভিত্তিতে একটি চাকরি করতে পারিনা। না ঘুষের কাছে আমার জ্ঞান অনেক ছোট। এর জন্য দায়ী কে?  সরকার  না আমি।,0,celebrity
সাড়ের দাপি যেন মানা হয় ।,0,celebrity
আপনার সাথে একমত। তবে আপনি যা লিখলেন তা প্রেমিকাকে পত্র লেখার মতোই হলো!! আমরা আরো কড়া ভাষায় লিখবেন আশা করছিলাম! ধণ্যবাদ দিতে পারলাম না।,0,celebrity
আগামীকাল জুম্মাবাদ শাহবাগে আপনার গায়েবী জানাজা হবে।,0,celebrity
অসাধারণ...,0,celebrity
দালালী ছাড় জাফর ইকবাল,0,celebrity
আরে স্যার আপনি বেচে আছেন?   আমি তো আপনার গায়েবী জানাজায় যাচ্ছিলাম 😂,0,celebrity
"পাশে থাকলে পাশে পাবেন।লাইক কমেন্ট করছি। ব্রেক করেন,লাইক কমেন্ট দেন",0,celebrity
সাঁর আপানাকে জবাই করেনি কেন,0,celebrity
স্যার আপনার লজ্জা লাগে না!!  এভাবে নিজেকে অসম্মানিত করবেন না।,0,celebrity
সুরমা জাহিদ  ৩৬১ বীরাঙ্গনাকে নিয়ে ‘বীরাঙ্গনা রচনা সমগ্র’ যার বয়স ১৯৭১ সালে ছিল ২ বছর। আর আপনি যুবক হওয়েও কেন যাত্রাবাড়িতে লুকিয়ে ছিলেন আর বাচ্চাদের নিয়ে গর্ত (আপনার ভাষায় ট্রেঞ্চ) খুরে লুকাই ছিলেন। ঠিক বুঝলাম না।চেতনাটা কই ছিল তখন?    #গর্ত_বীর,0,celebrity
মুক্তিযুদ্ধ এর সময় আপনি মাতুআইল এ লুকিয়ে ছিলেন কেন?,0,celebrity
খোদারে ডরাও মিয়া মইরাও শান্তি দিবা না?  চিন্তা করছিলাম আপনার চল্লিশায় জিলাপী খামু জুটলো না আপনি নরকেও ঠাই পাইবেন না খোদার কাছে বিচার দিলাম🙃,0,celebrity
"যদি এমন হতো, শুক্রবার সকালে ঘুম ভেঙে দেখতাম স্যার একটা পোস্ট দিছে এবং অল্প কথায় যার মর্মার্থ অনেক বেশি, এবং সেটি হতো মানবতা ও ন্যায়ের সাথে, সাথে দেশের প্রকৃত অবস্থা নিয়ে তবে কতইনা ভালো লাগতো।",0,celebrity
ঘটনার এতদিন পরে এসেও আসল সত্যটা আপনি জানতে পারলেন না। আফসোস! বড়ই আফসোস!,0,celebrity
ওমা! মঙ্গল গ্রহ থেকে কবে ফিরলেন?? ঐইখানের ধান্ধা কি শেষ??,0,celebrity
"sir সুন্দরবনে তেলের জাহাজ ডুবেএলাকায় তেল ছড়িয়ে পড়ল ৷ সেখানকার মানুষ খালের পানি খেয়ে থাকত ৷ সেই পানিতেও তেল ছড়িয়ে পড়েছে ৷ সুন্দরবনের যে অংশে তেল ছড়িয়ে পরেছে সেখানে নানা ধরনের মৃত মাছ পাওয়া গেছে ৷ একটা মাছরাঙা পাখি ঐ পানিতে পরে ডুবে যাচ্ছিল ৷ এক ছেলে তা দেখে পাখিটিকে উঠিয়ে নিয়ে আসে কিন্তু উঠানোর পর পাখিটা বেচে গেলেও ঐ পাখির গা পুড়ে পাখির গায়ের রঙ নষ্ট হয়ে গেছে ৷ পাখিটা কালো হয়ে গেছে তার রঙিন দেহ আর নেই ৷ কিন্তু এই পশুপাখিগুলো নিয়ে ঐ এলাকার পানির অভাবে থাকা মানুষগুলো নিয়ে কারও তেমন চিন্তা নেই ৷আজ ১৯ ডিসেম্বর আমাদের কলেজে জাতীয় পর্যায়ের বিজ্ঞান মেলা হচ্ছে ৷ বিভিন্ন কলেজ থেকে নানা project এসেছে ৷ কিন্তু ঐ সুন্দরবনের তেল অপসারণের পদ্ধতি নিয়ে কোন project nai.  কারণ আমরা ঐ বিষয় নিয়ে চিন্তাই করি না ৷ আমরাই তো তাদের বলার সুযোগ করে দেই যে আমাদের চিন্তা মৃত হয়ে গেছে ৷ আমরা আমাদের দেশের সব somossa nia চিন্তা করলে,  এইসব সমাধান করলে কে বলার সাহস পায় যে আমাদের চিন্তা মৃত ৷",0,celebrity
"অনেক মিস করছি এই মানুষটাকে। আজ যদি উনি বেচেঁ থাকতেন, উনি নিশ্চই এই কোমলমতি ছাত্রছাত্রীদের পাশে এসে দাঁড়াতেন। ওপারে ভাল থাকবেন স্যার...",0,celebrity
১৯৭১ সালে কোনো এক দেশপ্রেমিক গর্তে ঢুকে যুদ্ধ করছিল!!,0,celebrity
সব গুলা ict মামলায় পরবি। :),0,celebrity
"আল্লাহ্ বাচ্চাগুলোর সহায় হোন.... এই দোয়া ছাড়া আর কিছু করতে পারবোনা আমি।আমি ওদের পাশে  দাঁড়াতে পারলেও কিছু আসতো যেতোনা হয়তোবা ওদের। কারন আমি বিশেষ কেউনা,কিন্তু আপনি?একটিবারকি বাচ্চাগুলোর পাশে গিয়ে দাঁড়ানো যেতনা?খুব কঠিন ছিল ব্যাপারটা?লিখাটাও ভালো লেগেছে সত্য তবে আপনি সাধারন কেউনাযে কেবল এটা নিয়ে লিখেই দায়িত্ব শেষ বলে মনে করবেন।আপনাকে পছন্দ করি স্যার,সে পছন্দটাকে এমন দু-একটা ছোট-খাটো কাজ করে ভীষন রকমের পছন্দে আনা যায়না? .",0,celebrity
আসলে তিনি সেলিব্রিটিত তাই যা মন চায় তাই বলেন।,0,celebrity
"আজ আমি আবেগাক্রান্ত নই, আমি হতবিহল নই নই, বাস্তবতাকে মেনেনেয়ার প্রাণপোন লড়াই করে যাচ্ছি, স্যার, স্বপ্নের বাংলাদেশ গড়ে তোলার যে স্বপ্ন আপনি আমাদের মত তরুনদের মনে জাগিয়ে তুলেছেন, আমি মনেপ্রাণে বিশ্বাস করি, সেই স্বপ্ন আমরা পূর্ণ করবো, একদিন না একদিন করবোই, ",0,celebrity
"স্যার, এই ঘাতক বাস ড্রাইভার, মালিকদের দেখলে, তাদের কথা শুনলে আপনার বমি পায় না???",0,celebrity
স্যার ডাবল স্ট্যান্ডবাজি এবার খেমা দেননা। আপনিওতো মুক্তিযুদ্ধবিরুদী রাজাকার পরিবারের সন্তান আবার নিজেও মুক্তিযুদ্ধে অংশগ্রহণ না করে ভয়ে গর্তে লুকিয়ে ছিলেন! অথচ এখন আপনি মুক্তিযুদ্ধের চেতনার দোকান খুলে বসে আছেন এগুলো কি হিপোক্রেসি নয় স্যার? আপনার নানা আর আপনার বাপওতো রাজাকার ছিল। বঙ্গবীর কাদের সিদ্দিকি নিজের মুখে বলেছে এইকথাগুলো। অস্বীকার করতে পারবেন?,0,celebrity
"স্যার একটা অটোগ্রাফ দিবেন...... আপনার পরবর্তী বউ এর জন্য """"আমি দুর্বল""""",0,celebrity
আরে  রে  রে  উনি  আসছেন  অভিজিৎ   এর  গুনগান  গাইতে  ।  ধর্মান্ধ   কাপুরুষ   মানে  কি  বুঝিয়েছেন  জানিনা  ?  আল্লাহ   আর  আল্লাহর  নবীজীকে  নিয়ে  কটুক্তি  করবে  আর   উনি  এমনি  এমনি  বেঁচে  যাবেন  ।  আল্লাহ  এসব  নাস্তিকদের    এভাবে  করুণ   লাঞ্ছনার   মাধ্যমে   এই  দুনিয়া  থেকে  নিয়ে  যাবেন  ।  এসব  নাস্তিকদেরকে  না  মারলে  দিনে  দিনে  দিনে  আরো   নাস্তিক  বাড়বে   ।  তাই  আমি  মনে  করি  এসব  নাস্তিক  কুত্তাদেরকে  এভাবেই  মারা  উচিত।   আর  আশা  করি  আপনি  একজন  মুসলমান   হয়ে  আর  অভিজিৎ   রায়ের  মত  নাস্তিকদের  গুনগান   গাইবেন  না  ।,0,celebrity
"স্যার, আপনি এই পোস্ট করার আগেই আপনার পক্ষ থেকে হুবহু একই টাইপের পোস্ট অনেক মেধাবী ছাত্ররাই করেছে। এদেশের ছাত্রগণ আপনাকে কত্ত ভালোবাসে দেখেন। আপনার নাড়ী নক্ষত্র তারা চিনে ফেলেছে। ধন্য আপনি, ধন্য আপনার শিক্ষকতা জীবন। আপনাকে দেখে হিংসে হয়। ঝোপ বুঝে কোপ মারতে পারেন ভালো :3",0,celebrity
দূর্ঘটনা বশত জম্ন নেওয়া একটা সুবিধাবাধী অমানুষ,0,celebrity
আপনার কথায় একমত স্যার!,0,celebrity
"ব্যালেন্স করার এক অতি প্রাকৃত ক্ষমতা আছে আমাদের জাফর স্যারের।উনি সবাইকেই খুশি রাখার চেষ্টা করেন,আর সবাইকে খুশি রাখার চেষ্টা করে মূলত চাটুকাররাই।।",0,celebrity
আমাদের প্রিয় দেশটির ভবিষ্যত যে কত সুন্দর সেটি সবাই অনুমান করতে পারে কী না আমি জানি না। অল্প কিছু দায়িত্বহীন কিন্তু গুরুত্বপূর্ণ জায়গায় বসে থাকা মানুষের জন্যে আমরা আমাদের সেই সুন্দর ভবিষ্যতটি কিছুতেই নষ্ট হতে দেব  না। যদি কেউ চেষ্টা করে কাজ হোক আর না হোক ভাঙ্গা রেকর্ডের মতো আমি চিৎকার করতেই থাকব! Salut u Sir,0,celebrity
"আমাদের হাগু করার সিস্টেম যেহেতু আন্তর্জাতিক মানের নয়,তাই যুদ্ধাপরাধ বিচারটাও আন্তর্জাতিক মানের হওয়ার দরকার নেই… হা হা হা হা কত হাই লেভেলের বৈগ্যানিক চিন্তাভাবনা দেখেছেন? এই নাহলে ড্রোন বিগ্যানী! যাইহোক,জাফর ইকবালের কাছে 'কিন্তু' সম্পর্কিত ক'টি বৈগ্যানিক প্রশ্নঃ ১/ যুদ্ধাপরাধী তো আওয়ামীলীগেও আছে। এমনকি হাসিনার বেয়াই একজন সর্বজন স্বীকৃত রাজাকার, কিন্তু..….… ২/ ৭১ এ যে ধর্ষনগুলো হয়েছে তার বিচার চাইছেন,এখন লিটন পরিমলরা যে ধর্ষণে সেঞ্চুরী করে মিষ্টি বিতরন করে তার কি হবে? ও হ্যাঁ, তারা ধর্ষনে সেঞ্চুরী করলেও তারা কিন্তু..…..…? (সোনার ছেলে)?  ৩/ আপনার বাবার হত্যাকারীদের বিরুদ্ধে আদালতে সাক্ষী দিতে আসলেন না কিন্তু..…..…? ৪/ এখন চেতনার বাহাদুরী দেখান,অথচ ৭১ এ আপনি পরিপূর্ণ যুবক থাকা সত্বেও যুদ্ধে গেলেন না,কিন্তু..……? (খাটের তলায় লুকিয়ে ছিলেন) কৃতজ্ঞতা :উকিল চাচা",0,celebrity
"স্যার, জাতি আপনাদের ভাল করে চিনে, নিজেকে যদি সম্মানিত ব্যক্তি মনে করেন, লজ্জাবোধের লেশটুকুও যদি আপনার থাকে তাহলে চেতনামাইসিন টেবলেট না এনে শ্রীপুরের আদি আসল বাতের টেবলেট নিয়ে রাস্তায় বসে যান, অন্তত কবিরাজ বলে কিছুটা হলেও মানুষ সম্মান করবে। বাংলার মানুষ কে পাগল ছাগল মনে করেন নাকি যে আপনারা যা বলবেন তাই বিশ্বাস করবে?   আপনার চেতনা  এখন মল মেশানো এক ছেড়ে তেনা। জনগণ এটাকে এখন দুর্গন্ধের জিনিস মনে করে।  কোন দামী বংশের উপাধি দিয়ে যদি সারাজীবন ফষ্টি নষ্টি করেও কেউ মনে করে যে আমরা উচ্চ বংশের তবে চেতনা উপাধি নিয়েই আপনারা তাই করতে পারেন।",0,celebrity
"কতটা ব্রেইন ওয়াশড এবং বিকৃত মানসিকতার মানুষ এই দেশে এখনো বাস করছে (কমেন্ট সেকশন দ্রষ্টব্য), সেটা দেখে ভয় হয়...",0,celebrity
"স্যার ১ তারিখের লেখা পোস্ট ৩ তারিখে কেন?????? স্যার যদি কোদাল লাগে বইলেন, আমার বন্ধুরা আপ্নার ক্যাম্পাসের রানিং স্টুডেন্ট......",0,celebrity
অবশ্যই বিশ্ববিদ্যালয়ের নিজস্ব নিয়মে চলবে,0,celebrity
"অাপনাকে অাগে অনেক সম্মান করতাম, এখন অার করিনা। কারন অাপনি একটা চেতনাবাজ।",0,celebrity
"...আমাদের এই বাংলাদেশের প্রতিটি sector-এ  রন্ধ্রে রন্ধ্রে এমনভাবে দুরনীতি ঢুঁকে গেছে যে যখনই সবকিছু চিন্তা করি তখনি সবকিছু ওলটপালট লাগে, এক অজানা ভয়ংকর রকম কষ্ট হয়, প্রতিবারই চোখের কোণায় জলে ভরে যায় আর আমি কোন সমাধান খুজে পাই না। আচ্ছা আজকের এই দেশটা পাওয়ার জন্নই কি এতগুলো মানুষ তাদের জীবন দিয়েছিল???? আমাদের দেশের এইসব মহান দেশ্নেত্রীরা কবে এই দেশটাকে সত্যিকারের ভালবাসবেন কেউ কি বলতে পারেন?????",0,celebrity
"আমাদের দেশের অধিকাংশ মানুষ আত্মকেন্দ্রীক  একারণে বললাম, তা না হলে কী এত পার্থক্যের সৃষ্টি হয়   প্রতিটি প্রতিষ্ঠান ও তার অঙ্গগুলো সব নিজেদের নিয়ে ব্যস্ত জানি স্যার আপনার ব্যক্ততাগুলোও স্বার্থের নীচে চাপা দিতে ওরা ব্যস্ত  ",0,celebrity
"জাফর ইকবাল স্যার আর আমাদের মাঝে নেই, ঊপারে ভালো থাকবেন স্যার 😂😂 সূত্র উইকিপিডিয়া",0,celebrity
গল্পের নামঃ বাবা লেখকঃ রায়হান পারভেজ। লিংকঃ https://m.facebook.com/story.php?story_fbid=962813160536430&id=747873045363777,0,celebrity
মূর্খ,0,celebrity
গর্তের ভিতর থেকে বের হইসে এটলাস্ট,0,celebrity
সেকুলাঙ্গার,0,celebrity
আমাদের দেশে সবই সম্ভব।।,0,celebrity
খুবই মহৎ  উদ্যোগ স্যার ❤👌,0,celebrity
তারিখ ২/৮/২০১৮,0,celebrity
"……………….আমাদের এ ক্ষুদ্র প্রয়াসে পাশে থাকুন…………………….. প্রিয় বন্ধুগণ,   আওয়াজ দেন।ভাষাশহীদের আত্মত্যাগের এ মাসে ,যুদ্ধ অপরাধির ফাঁসির দাবিতে, উত্তাল এ সময়ে- গর্জে উঠুক কণ্ঠ সাথে কলম,কালি ও তুলি। তাইতো এ আন্দোলনকে বেগবান করতে তরুণ সমাজ রাংপুর এর আয়োজনে একটি দেয়ালিকা প্রকাশের পথে । তাই আর পিছিয়ে নয়,১৮ ফেব্রুয়ারী'র মধ্যে বিষয় ভিত্তিক ও সমকালীন ছড়া,কবিতা,অনুগল্প,প্রবন্ধ এবং আপনার আঁকা কার্টুন,কমিক্স,ছবি সহ সুচিন্তিত মতামত দিন Anari Karigor এই আইডিতেই অথবা   যোগাযোগঃ  জিয়াউল আলাম ফারুকী হক হোমিও হল, বাংলাদেশ মসজিদ মিশন, জাহাজ কোং মোর।  স্টেশন রোড,রংপুর-৫৪০০  অথবা  মালেক মামার টি স্টল, ম্যাকের মোর্‌ রংপুর সরকারি কলেজ রোড,রংপুর-৫৪০০ ই-মেইল করুন mohakal.21@gmail.com প্রয়োজনে:01915215642",0,celebrity
অল্পসময়ে গালমন্দ শেখার জন্য এই পেইজটা উপযুক্ত😛😂😂,0,celebrity
এ বোকাচোদা কোপ এমনি এমনি খায়না। পুরাই গন্ডার,0,celebrity
আপনার স্টাটাস টা দেখে ডিম থেরাপির কথা মনে পড়ে গেল স্যাঁড়। সব দিন কি আর ভাল যায় কখনো দিন খারাপ ও যেতে পারে তাই ডিম খাবার অভ্যাস করুন পরবর্তীতে কাজে দিবে।,0,celebrity
"স্যার, আপনার লেখায় সবাই হাহা দেয় কেন? এতে আমার ভীষণ কষ্ট হয় স্যার। কাঁদতে চাইলেও কান্না আসে না।   আপনার লেখা আমার ভীষণ ভালো লাগে স্যার। আমি আপনার ভীষণ ভক্ত স্যার। দোয়া করি আপনি আরও ভালো তেল মারুন উপরমহলকে।",0,celebrity
"বিশ্ববিদ্যালয় শিক্ষকদের টাকার লোভ তো হবেই,সবাই তো আর আপনার মতো সরকারের দালালী করে পয়সা উপার্জন করেনা|",0,celebrity
"শহিদুল অালমের বক্তব্যটা শুনেন স্যার। অাপনি জ্ঞানী মানুষ, বুঝতে পারবেন তিনি সমালোচনা করেননি, যা বলেছেন তা স্পষ্ট মিথ্যাচার। অাপনি হয়তো ভুলে গেছেন স্যার, এই ব্যক্তি জিয়াউর রহমানকে স্বাধীনতার ঘোষক বানাতে নকল কন্ঠস্বরেরও ব্যবস্থা করেছিলেন!  স্যার, অাপনি জ্ঞানী মানুষ, জাতির বিবেক, অাপনার কলমে কেন দেশবিরোধীদের জন্য সহানুভূতি অাসবে?  স্যার, পরিশেষে এটাও জানাতে হচ্ছে,  রাজাকারদের পেইড এজেন্ট ডেভিড বার্গম্যানের কষ্টে (!!) যারা উদ্বিগ্ন হয়েছিলেন, শহীদুল অালম তাদেরই একজন!   এই লোক অাওয়ামী লীগের দুর্নাম গাওয়ার সুযোগ পেলে কী ছেড়ে দিবে স্যার?",0,celebrity
"স্যার, আপনার জন্য শ্রদ্ধা আর ভালবাসা অনিশেষ।  যে যাই বলুকনা কেন, যেভাবেই রি এ্যাক্ট দিক না কেন, ড.মোহাম্মদ জাফর ইকবাল বাংলাদেশের গর্ব, এটা কি কেউ মুছে ফেলতে পারবে বা পেরেছে এই সব সমালোচনা আর বাজে রি এ্যাক্ট দিয়ে ??? এটাই বাস্তবতা। আমরা বা  ড. মোহাম্মদ জাফর ইকবাল স্যার এগুলোতে কক্ষনই বিচলিত হইনা।",0,celebrity
আপনার পোস্টটা গুজবের খাতায় নাম লেখানোর যোগ্যতা রাখে। কেন?  কারণ আপনি কিছুই জানেন না! তবুও লিখতে বসছেন।  আপনি কি Jon Snow এর দাদা????   You know nothing Zafar sir! 🐸,0,celebrity
মতামত দাও 😷 Iqbal Hasan,0,celebrity
মুক্তিযেদ্ধের চেতনা বিহীন স্যারের লেখা পড়তে ভালা লাগেনা!,0,celebrity
"স্যার কবি, সাহিত্যিক, লেখকদের কলমের শক্তি নাকি অস্রের চেয়েও বেশি । স্যার তবে কি আপনি শুধু কলমের শক্তি দেখাতে পারবেন? ক্ষুদ্র মস্তিষ্কের অধিকারি হয়েও নিজের মত আপনাকেও নন্দলালের মত লাগছে।এগিয়ে যান কলম নিয়ে।নেশা কাটলে ফিরবেন?",0,celebrity
"আমি রাজাকার"" ছাত্ররা মতিয়া চৌধুরীকে ট্রল করার জন্য লিখেছিলো, সেইটা খুব ভালোভাবেই জানেন আপনি। তারপরেও দালালী করার জন্য খুব ভালোভাবেই উপস্থাপন করেছেন। মতিয়া চৌধুরী সংসদে দাঁড়িয়ে যখন আন্দোলনকারীদের সবাইকে যখন রাজাকার বানিয়ে দিলেন, তখন তো চুপ ছিলেন",0,celebrity
নতুন নতুন জোক্স পেতে এই পেইজের সংগেই থাকুন :),0,celebrity
আপনার সমস্যা স্যার আপনি তৈরি করেছেন। কথাটা একটু কষ্টদায়ক মেনেনিন তা না হলে আমরা লেখা শিখব কিভাবে। আপনার মেধাবী ছত্র-ছত্রীদের আপনার পিছনে দাঁড়াতে উৎসাহ দেন। মন্দদের রাজত্ব ধ্বংস করতে হলে ভালো সমাজ তৈরি করুন স্যার।,0,celebrity
মুক্তিযুদ্ধের  সময় তো স্যার আপনার যোদ্ধে যাবার বয়স ছিল । তখন তো পাড়িয়ে বেড়িয়েছেন । তখন মুক্তিযুদ্ধে যোগ দিতে পারতেন ।   এখন এসব কথা অপনার মুখে শুভা পায় না,0,celebrity
বেচারার বই আর পাবলিক খাবেনা বলে ওস্তাদজি একটু চেতনা শিখাতে আসছে☺,0,celebrity
জয় বাংলা,0,celebrity
আল্লাহ  উনাকে  বেহেস্ত  নসীব করুন।,0,celebrity
"অসাধারণ  লেখা। আমাদের দেশের উন্নতি করতে হলে অবশ্যই শিক্ষাব্যবস্থায় একটা পরিবর্তন আনা দরকার। আমাদের দেশে ভাল কাজের সন্মানী খুব কম যেটা শিক্ষকদের অবস্থা দেখে বোঝা যায়। শুধু তাই নয়, আমাদের দেশে পরীক্ষা নিয়ে এক প্রকার চাপ  শিশুদের মাঝে সৃষ্টি করা হয়। এটি এমন চাপ, যার ফলেই শিশুরা বাধ্য হয় ফাঁস  হওয়া প্রশ্ন দেখতে। সবাই শিশুদের কাছে ভাল ফল প্রত্যাশা করে যার ফলে তার  উপর চাপ সৃষ্টি হয়। ফলে সবাই চিন্তা করে কীভাবে ভাল ফল করা যাবে, কেউ এটা  চিন্তা করে না যে কীভাবে জ্ঞান অর্জন করা যাবে। আজকাল লেখাপড়া এমন এক  পর্যায়ে চলে গিয়েছে, যেখানে মানুষ পড়ে পরীক্ষায় ভাল ফলের জন্য আর ভাল  বেতনের চাকরীর জন্য। কেউ জ্ঞান অর্জনের জন্য পড়ে না। এর সমাধান হচ্ছে  শিক্ষাব্যবস্থার পরিবর্তন। আর বর্তমান শিক্ষামন্ত্রী মনে করেন, ডায়রিয়া হলে  টয়লেটে যাওয়া বন্ধ করতে হবে বা মাথা ব্যথা হলে মাথা কেটে ফেলে দিতে হবে।  তাই তিনি কোচিং বন্ধ করতে লটারীর মাধ্যমে ভর্তির ব্যবস্থা করেছেন আবার  প্রশ্ন ফাস বন্ধে ফেসবুক বন্ধ করে দিতে চান। এটি মোটেও কোনো সমাধান নয়।  আমাদের দেশের সব শিক্ষার্থী যদি জ্ঞান অর্জনের লক্ষ্যে পড়ে, তবে এদেশ অতি  দ্রুত উন্নতির পথে এগিয়ে যাবে।",0,celebrity
মদ খা বুদ্ধি বাড়া ওকে?,0,celebrity
স্যার আপনি সার্কাজম বোঝেন না *_* আপনি মালকোভার কাছে যান :( :(,0,celebrity
"ভেবেছিলাম হসপিটাল থেকে আসার পর আপনি সুস্থ্য হয়েছেন। এখন দেখি পুরোপুরি সুস্থ্য হন নাই, ওষধ ঠিকমতো খাচ্ছেন না??",0,celebrity
সার আপনার কী বমি থেমেছে? আপনার মানবতার আম্মা রাগ করবে না? লেখাগুলো দেখে।,0,celebrity
যুদ্ধে না গিয়া পাকিদের কাছ থেকে বাচাঁর জন্য নীলক্ষেতে গিয়া চুল কাটেন।😃😃😃 ছি। ৭১ এ নাকি গর্তে ছিলেন?????,0,celebrity
"যে ছেলেটাকে নামাজের কথা বলায় জাফর স্যার পুলিশে দিয়েছেন তার সাথে আসলে কী হবে?  কিছুই হবে না। ঘটনাটা পত্রিকাসহ সামাজিক যোগাযোগ মাধ্যমগুলোয় যেভাবে ছড়িয়ে পড়েছে তাতে করে মিথ্যা মামলা দিয়েও ছেলেটা কে আটকে রেখে খুব একটা সুবিধা পুলিশ করতে পারবে না। ঘটনা এখানে পানির মত পরিস্কার। ওয়াটার ইজ কিলিয়ার হিয়ার।  কিন্তু এ ঘটনায় স্যারের কী হবে? তার মর্যাদা আর ভালোমানুষির মুখোশটা আরও একটু ঢিল হয়ে যাবে এবং তা গেছেও নিশ্চিতভাবে। তার সাথে ঘটে যাওয়া সাম্প্রতিকালের।প্রতিটা ঘটনায় তিনি নিজেই নিজের দ্বিমুখীতার প্রমাণ দিয়ে গেছেন বারবার।  কয়েক বছর আগে তার স্ত্রীসহ শাবিপ্রবির শিক্ষকেরা যখন ছাত্রলীগের হাতে হালকা করে পিটুনি খেলো। তখন তিনি এর তৎক্ষণাত প্রতিবাদ স্বরুপ সকাল বেলা বৃষ্টি বিলাস করে এবং পরদিন এক বিরাট বার্তা দিয়ে জাতিকে জানান দিলেন ছাত্রলীগের ছেলেরা বাবুমানুষ, ওরা মাঝে মধ্যে নিডো দুদু (১ থেকে ৩ বছরের কৌটার) খায়। ওদের মাথায় হাত বুলায় দিলে ওরা ভালো হয় যাবে। আমার কাছে পাঠান ওদের।  এছাড়া প্রশ্নপত্র ফাঁসের জন্য সকাল বেলা শিক্ষামন্ত্রীর বিরুদ্ধে আন্দোলন করে সন্ধ্যাবেলায় শিক্ষামন্ত্রীর কাছ থেকে পুরস্কার নেয়ার ঘটনাটা এখন আর বললাম না। :p  এর কিছুদিন পর তিনি বুঝতে পারলেন মুক্তিযুদ্ধ মুক্তিযুদ্ধ ব্যবসাটা মন্দের দিকে; কেউ আর তেমন গুরুত্বপূর্ণ দিচ্ছে না। ব্যবসা চাঙা করতে তার ট্রেঞ্চ খননের বীরত্বগাঁথা রচনা করলেন। কথায় আছে বিপদ আসলে চারদিক থেকেই নাকি আসে। তার বীরত্বগাথার  ফলাফল হল উলটো। গাল খেলেন হরদম। বাম-সেকুলার-ইসলামপন্থী কেউ আর তেমন বাকি রাখেননি বেচারাকে তুলোধুনো করতে। আরও কিছু ফ্যানবয় হারালেন স্যার। (জিভ দিয়ে চুকচুক করে আফসোসের আওয়াজ হবে)  কোন এক অতি উৎসাহী ছেলে বোকার মতো একদিন গিয়ে স্যারকে কাস্টার্ড কেক ভেবে কোপ দিয়ে বসলো। এ সুযোগ তিনি হাতছাড়া করতে চাইলেন না। নিজের লেখনি আর কর্মকান্ডের দ্বারা মুসলিম সংখ্যাগরিষ্ঠ জাতির কাছে যে সমালোচনার স্বীকার হয়েছেন তা থেকে একটু মার্কেট উপরে উঠিয়ে জাতে উঠার এই এক সুযোগ। তিনি এক মহান বক্তব্যে আমাদের জানালেন তিনি কুরআন পড়েন। তিনি মুসলিম।  স্যার ভালো অভিনয় জানেন। কিন্তু অভিনয় ব্যাপারটা দীর্ঘ সময় ধরে রাখার কৌশলটা এখনও তেমন রপ্ত করতে পারেননি। তিনি মুখোশ পড়ে থাকতে পারলেন না। তার অন্তরে থাকা বিষ, ইসলামের প্রতি ঘৃণা তাকে বাধ্য করলো মাস দুয়েক না গড়াতেই নামাজের কথা বলায় একটা ছেলেকে জেলে দিয়ে দিতে।  স্যার আপনার দৃষ্টিতে যদি নামাজ পড়া খারাপ বা ভয়ংকর কিছু হয়ে থাকে তবে ছেলেটাকে কি ছাত্রলীগের দুদু খাওয়া বালকদের মত মাথায় হাত বুলিয়ে বুঝিয়ে বললে চলত না? একেবারে জেলে দিয়ে দিতে হবে? বিশ্ববিদ্যালয় পড়ুয়া একটি নির্দোষ ছেলের জীবনে জেল খাটা আসামীর যে কালিমা আপনি লাগিয়ে দিলেন এর দ্বায় কে নেবে? নেবেন আপনি? লজ্জার মাথা কি এতটাই খেয়ে ফেলেছেন?  স্যার আপনি বলেছেন আপনি অতি মনোযোগ সহকারে কুরআন পড়েছেন। হয়তো এই আয়াতগুলো খেয়াল করেননি। আরেকবার একটু পড়ে দেখবেন কি?",0,celebrity
আপনার ভোট কি আপনি দিতে পেরেছেন জাতি জানতে চায়?,0,celebrity
"জাফরের পেজে সবাই আনলাইক দিয়ে প্রতিবাদ জানাও,,,এবং এর বইগুলো কুরিয়ার করে তার কাছে পাঠিয়ে দেও... ঠিকানাঃ- মুহাম্মদ জাফর ইকবাল শাহাজালাল বিঞ্জান ও প্রযুক্তি বিশ্ববিদ্যালয়",0,celebrity
স্যার উ গ্রেট,0,celebrity
"বইমেলা একটি সাম্প্রদায়িক মেলা, এখানে শুধুমাত্র একটি বিশেষ গোষ্ঠীর বই  প্রকাশিত হয় এবং বইয়ের স্টল দেয়া হয়,,এরকম একটি দেশের প্রতিনিধিত্ব করতে পারে না! সময়ের প্রতিনিধিত্ব করতে পারে!!",0,celebrity
"ওয়াক থু,,  দাদাল",0,celebrity
অসাধারন!! অামার ছেলেকে সবসময় অাপনার কথাই বলি!  রাজাকারের বাচ্চারা কেনো এখানে এসে  বিরক্ত করে বুঝি না!  অারে তোদের স্থান হচ্ছে  ডাস্টবিনে!,0,celebrity
খুবতো মুক্তিযোদ্ধা বলে চিল্লাইলেন।মুক্তিযুদ্ধের সময় আপ্নার ভূমিকা কি ছিল বলেনতো জনাব।,0,celebrity
চাটুকারিতার টাকা কি আপনি বিকাশে নেন নাকি কেশ (চুল) এ?,0,celebrity
"দ্বিতীয় যে এয়ারপোর্টে আমি যথেষ্ট স্বস্তি অনুভব করি, সেটি হচ্ছে নিউ ইয়র্কের এয়ারপোর্ট। এখানেও বাঙালি পুলিশ অফিসার ইমিগ্রেশনের লাইনে মানুষকে নিয়ন্ত্রণ করেন। তাঁরাও আমাকে চিনে ফেলেন এবং আলাদাভাবে সাহায্য করেন। কাজ শেষ হওয়ার পর তাঁরা আমার সঙ্গে একটি সেলফিও তুলে ফেলেন। আমাদের সঙ্গে যেহেতু একটি ছোট শিশু ছিল, তাই এয়ারপোর্টের অপরিচিত মানুষরাও নিজ থেকে এগিয়ে এসে আমাদের সাহায্য করে। যেখানে মানুষজন লম্বা লাইনে দাঁড়িয়ে আছে, সেখানে আমাদের কখনো লাইনে দাঁড়াতে হয় না। ছোট শিশুকে সম্ভাব্য সন্ত্রাসী হিসেবে না দেখে ছোট শিশু হিসেবেই দেখার মধ্যে নিশ্চয়ই এক ধরনের আনন্দ আছে, অন্য এয়ারপোর্টের সিকিউরিটির মানুষরা কখনোই সেই আনন্দটি উপভোগ করতে পারে না। নিউ ইয়র্ক শহরটি নিঃসন্দেহে একটি চমকপ্রদ শহর। যারা এই শহরে থেকেছে কিংবা ঘুরতে এসেছে, সবাই এটি স্বীকার করবে। একেকজন মানুষের কাছে শহরটিকে একেকটি কারণে চমকপ্রদ মনে হতে পারে; যেমন—আমার কাছে এই শহরকে চমকপ্রদ মনে হওয়ার অনেক কারণের একটি হচ্ছে, এখানকার মানুষের শরীরের উল্কি (tattoo)! শীতকালে জাব্বাজোব্বা পরে শরীর ঢেকে রাখতে হয় বলে বেশির ভাগ সময় উল্কি দেখা যায় না। গ্রীষ্মে বা গরমের সময় এখানকার মানুষের উল্কি উপভোগ করা যায়। শৈশবে শুধু এক রঙের উল্কি দেখেছি; কিন্তু উল্কি যে কত বিচিত্র রঙের হতে পারে এবং কত নান্দনিক হতে পারে, সেটি এখানে না এলে কেউ অনুমান করতে পারবে না",0,celebrity
আল্লাহ আমাদের দেশের সবাই কে হেদায়ত দাও দুনিয়ার কথা ছেরে আখাতের কথা চিন্তা করোক সবাই। দুনিয়াতে সারাজিবন বেচে থাকার ক্ষমতা কারো নেই,0,celebrity
থাক ...আৱ বাকি অংশ পড়ছি নাহ 😂,0,celebrity
"স্যারের চুরি করা উপন্যাসগুলোর অন্যতম ""তবু ছোটাচ্চু তবুও টুনটুনি"" বেটা চুরিটাও ঠিকমত করতে পারেনি।শেষ পর্যন্ত ধরা খেলো।",0,celebrity
"ড. মুহাম্মদ জাফর ইকবাল.  তিনি ১৯৫২ সালের এই দিনে সিলেটে জন্মগ্রহন করেন। তিনি একাধারে শিক্ষক,পদার্থবিদ,,মুক্তিযোদ্ধা ,মুক্তিযোদ্ধা গবেষক,লেখক,কলামিষ্ট ও একজন বিজ্ঞানী। স্যার ব্যক্তিজীবনে ১ স্ত্রী ২ সন্তানের জনক। তার স্ত্রীর নাম ড. ইয়াসমীন হক, ছেলে নাবিল ইকবাল ও মেয়ে ইয়াশিম ইকবাল। স্যার ছোট বেলায় একজন মুক্তিযোদ্ধা ছিলেন। তিনি ড্রোন নিয়ে পাকিস্তানী হানাদার বাহীনির উপর ঝাপিয়ে পড়বেন এমন চিন্তা করেছিলেন,কিন্তু ড্রোন নিয়ে ঝাপিয়ে পড়ার আগেই দেশ স্বাধীন হয়ে যায়। স্যার এখনো এই দেশের মৌলবাদী,জামাতি, হেফাজতি জঙ্গী সংগঠন গুলোর বিরুদ্ধে যুদ্ধ করে যাচ্ছেন। স্যারের সব চেয়ে বড় পরিচয় তিনি একজন সফল সাহিত্যক। বাংলা সাহিত্য তার কাছে অনেক ঋনী। স্যারের লেখা বিশেষ করে সাইন্স ফিকশান গুলো সারা বিশ্বে এত জন প্রিয়তা পেয়েছে যে বিভিন্ন দেশের নামি দামী লেখক্গন তার লেখা চুরি করে। নিচে কিছু তার উদাহরন দিচ্ছি। ১) স্যার "" অবনীল "" নামক একটি বই প্রকাশ করেন ২০০৪ সালে। আর বইটি হবুহ নকল করে ২০০০ সালে জিম হুইট আর কেন হুইট নামে দুই ভাই মিলে "" পিচ ব্লাক "" নামে একটি হলিউডের সিনেমা বানিয়ে ফেলেন। ২) স্যার ১৯৯৯ সালে আরেকটি বই লেখেন "" নিতু তার বন্ধুরা ""। স্যারের এই বইটা নকল করে দানি দেভিতো নামে এক ভদ্র লোক "" ম্যাটিল্ডা "" নামে এক হলিউডের সিনেমা বানিয়ে ফেললেন ১৯৯৪ সালে। ছবিটি বাজেটের চেয়ে ৬৫ কোটি ডলার বেশি নিজের পকেটে ঢুকিয়েছেন অথচ স্যারকে একটি টাকাও দিলেন না। ৩) ঠিক তেমনি স্যারের ২০০৫ সালে বের হওয়া "" আমি তপু "" ১০ বছর আগে ১৯৯৫ সালে ডেবিড পেলজার নামে আমিরিকান এক সাহিত্যক নকল করেন। তার বইটির নাম দেন "" আ চাইল্ড কল্ড ইট "" ৪) স্যারের ২০০০ সালে বের হওয়া "" মেকু কাহিনী "" বইটি নকল করে ১৯৯৪ সালে প্যাট্রিক রিড জনসন নামে এক হলিউডের পরিচালক বানিয়ে ফেললেন বিশ্ব বিখ্যাত শিশুতোষ ছবি "" বেবিজ ডে আউট "" ৫) একই ভাবে স্যারের ১৯৮৮ সালে ট্রাইটন একটি গ্রহের নাম বইটি নকল করে ১৯৭৯ সালে বের করা হয় "" এলিয়ন ""। সারা বিশ্ব স্যারের বই নকল করে এ জন্য স্যার তিন তিন বার সাহিত্যে নোবেল পেলেও তিনি তা প্রত্যাখান করেন। ২০১৪ সাল একটি মাইলফলক হয়ে থাকবে বাংলাদেশের জন্য। এই বছরই স্যার বাংলাদেশে প্রথম আবিষ্কার করেন দ্রুত গতি সম্পন্ন ড্রোন। পেন্সিল ব্যাটারী চালিত এই ড্রোন ভুমি থেকে ১ হাজার মিলি মিটার উপরে উড়তে সক্ষম। আমেরিকার পেন্টাগন স্যারের এই ড্রোন কিনতে চাইলে স্যার দেশের স্বার্থে তা বিক্রি করতে চান নি। তবে এ বছরের শেষের দিকে আনসারুল্লাহ বাংলা টিম নেমে এক জঙ্গী সংগঠন স্যারের এই ড্রোন চুরি করলে সরকারের চৌকস গোয়েন্দা টিম তা উদ্ধার করতে সক্ষম হয়। স্যার অনেক সামাজিক, মানবাধিকার ও কল্যানমুলক সংগঠনের সাথে জড়িত, স্যার বিশেষ করে নারী অধিকার সংগঠনের হয়ে কাজ বেশি করেন।তিনি নারীদের অনেক সম্মান দেন ভালবাসেন। এ জন্য তিনি কোন ছাত্রের সাথে সেলফি ও ফটো সেশনে অংশগ্রহন করেন না। তিনি কোন ছেলেদের নাচেও যুক্ত হন না। সৌজন্যেঃ Abul Mal",0,celebrity
একমত ।,0,celebrity
"একটি স্বৈরাচারী ক্ষমতালোভী শাসকের জন্য সবচাইতে বড় হুমকি হচ্ছে শিক্ষিত জনগোষ্ঠী।  সুতরাং,  এটাই স্বাভাবিক যে ক্ষমতালোভীরা চাইবে একটি অশিক্ষিত,  স্বার্থপর ও দূর্নীতিবাজ জেনারেশন গড়ে উঠুক, যারা দেশ নয় ব্যক্তি স্বার্থের কথাই শুধু চিন্তা করবে। অন্যদিকে, সুশিক্ষিত মানুষ একদিন না একদিন শোষণ দূর্নীতি এবং অত্যাচারের বিরুদ্ধে প্রতিবাদ করবেই। এর প্রকৃষ্ট উদাহরণ ড. জাফর ইকবাল নিজেই। শুরু থেকেই বর্তমান সরকারের বিভিন্ন বিতর্কিত বিষয়ে তিনি হয় সরকারের পক্ষে সাফাই গেয়েছেন, অথবা মৌন ভূমিকা পালন করেছেন। কিন্তু, তিনি যেহেতু সুশিক্ষিত একজন মানুষ,  তাই আর চুপ করে থাকতে পারছেন না। মৃদু হলেও প্রতিবাদ করেছেন, তাই আপনাকে ধন্যবাদ ড. জাফর ইকবাল।",0,celebrity
"""শহিদুল আলম যেসব কাজ করেন, আমরাও আমাদের মতো করে সেসব করতে চাই, তারমত প্রতিভাবান বা দক্ষ নয় বলে করতে পারিনা ।"" কথাটা আমার নয়, বলেছেন শ্রদ্ধাভাজন অধ্যাপক মুহাম্মদ জাফর ইকবাল । আমরাও তাঁর সাথে সম্পূর্ণ একমত । প্রতিভাবান ও দক্ষ মানুষের কাছে জাতির প্রত‍্যাশা অনেক । কিন্তু ঐ প্রতিভাবান ও দক্ষ মানুষটি যদি এমন কোন অপকর্ম করেন যার জন‍্য জাতিকে অপরিসীম খেসারত দিতে হয় ও জাতীয় অস্তিত্ব হুমকির সম্মুখীন হয় তখনও কি তাকে জবাবদিহিতার আওতায় আনা যাবেনা ? এমনকি আপনিও যদি কখনও এমন কিছু করেন, আপনাকে কি কোন জবাবদিহি করতে হবেনা ? আশা করি জবাব এড়িয়ে যাবেননা, অধ‍্যাপক জাফর ইকবাল ।",0,celebrity
"যে ছেলেটাকে নামাজের কথা বলায় জাফর স্যার পুলিশে দিয়েছেন তার সাথে আসলে কী হবে?  কিছুই হবে না। ঘটনাটা পত্রিকাসহ সামাজিক যোগাযোগ মাধ্যমগুলোয় যেভাবে ছড়িয়ে পড়েছে তাতে করে মিথ্যা মামলা দিয়েও ছেলেটা কে আটকে রেখে খুব একটা সুবিধা পুলিশ করতে পারবে না। ঘটনা এখানে পানির মত পরিস্কার। ওয়াটার ইজ কিলিয়ার হিয়ার।  কিন্তু এ ঘটনায় স্যারের কী হবে? তার মর্যাদা আর ভালোমানুষির মুখোশটা আরও একটু ঢিল হয়ে যাবে এবং তা গেছেও নিশ্চিতভাবে। তার সাথে ঘটে যাওয়া সাম্প্রতিকালের।প্রতিটা ঘটনায় তিনি নিজেই নিজের দ্বিমুখীতার প্রমাণ দিয়ে গেছেন বারবার।  কয়েক বছর আগে তার স্ত্রীসহ শাবিপ্রবির শিক্ষকেরা যখন ছাত্রলীগের হাতে হালকা করে পিটুনি খেলো। তখন তিনি এর তৎক্ষণাত প্রতিবাদ স্বরুপ সকাল বেলা বৃষ্টি বিলাস করে এবং পরদিন এক বিরাট বার্তা দিয়ে জাতিকে জানান দিলেন ছাত্রলীগের ছেলেরা বাবুমানুষ, ওরা মাঝে মধ্যে নিডো দুদু (১ থেকে ৩ বছরের কৌটার) খায়। ওদের মাথায় হাত বুলায় দিলে ওরা ভালো হয় যাবে। আমার কাছে পাঠান ওদের।  এছাড়া প্রশ্নপত্র ফাঁসের জন্য সকাল বেলা শিক্ষামন্ত্রীর বিরুদ্ধে আন্দোলন করে সন্ধ্যাবেলায় শিক্ষামন্ত্রীর কাছ থেকে পুরস্কার নেয়ার ঘটনাটা এখন আর বললাম না। :p  এর কিছুদিন পর তিনি বুঝতে পারলেন মুক্তিযুদ্ধ মুক্তিযুদ্ধ ব্যবসাটা মন্দের দিকে; কেউ আর তেমন গুরুত্বপূর্ণ দিচ্ছে না। ব্যবসা চাঙা করতে তার ট্রেঞ্চ খননের বীরত্বগাঁথা রচনা করলেন। কথায় আছে বিপদ আসলে চারদিক থেকেই নাকি আসে। তার বীরত্বগাথার  ফলাফল হল উলটো। গাল খেলেন হরদম। বাম-সেকুলার-ইসলামপন্থী কেউ আর তেমন বাকি রাখেননি বেচারাকে তুলোধুনো করতে। আরও কিছু ফ্যানবয় হারালেন স্যার। (জিভ দিয়ে চুকচুক করে আফসোসের আওয়াজ হবে)  কোন এক অতি উৎসাহী ছেলে বোকার মতো একদিন গিয়ে স্যারকে কাস্টার্ড কেক ভেবে কোপ দিয়ে বসলো। এ সুযোগ তিনি হাতছাড়া করতে চাইলেন না। নিজের লেখনি আর কর্মকান্ডের দ্বারা মুসলিম সংখ্যাগরিষ্ঠ জাতির কাছে যে সমালোচনার স্বীকার হয়েছেন তা থেকে একটু মার্কেট উপরে উঠিয়ে জাতে উঠার এই এক সুযোগ। তিনি এক মহান বক্তব্যে আমাদের জানালেন তিনি কুরআন পড়েন। তিনি মুসলিম।  স্যার ভালো অভিনয় জানেন। কিন্তু অভিনয় ব্যাপারটা দীর্ঘ সময় ধরে রাখার কৌশলটা এখনও তেমন রপ্ত করতে পারেননি। তিনি মুখোশ পড়ে থাকতে পারলেন না। তার অন্তরে থাকা বিষ, ইসলামের প্রতি ঘৃণা তাকে বাধ্য করলো মাস দুয়েক না গড়াতেই নামাজের কথা বলায় একটা ছেলেকে জেলে দিয়ে দিতে।  স্যার আপনার দৃষ্টিতে যদি নামাজ পড়া খারাপ বা ভয়ংকর কিছু হয়ে থাকে তবে ছেলেটাকে কি ছাত্রলীগের দুদু খাওয়া বালকদের মত মাথায় হাত বুলিয়ে বুঝিয়ে বললে চলত না? একেবারে জেলে দিয়ে দিতে হবে? বিশ্ববিদ্যালয় পড়ুয়া একটি নির্দোষ ছেলের জীবনে জেল খাটা আসামীর যে কালিমা আপনি লাগিয়ে দিলেন এর দ্বায় কে নেবে? নেবেন আপনি? লজ্জার মাথা কি এতটাই খেয়ে ফেলেছেন?  স্যার আপনি বলেছেন আপনি অতি মনোযোগ সহকারে কুরআন পড়েছেন। হয়তো এই আয়াতগুলো খেয়াল করেননি। আরেকবার একটু পড়ে দেখবেন কি?",0,celebrity
স্যার আপনাকে অনেক দরকার এই দেশটাকে পরিপক্ব করতে,0,celebrity
আপনার Android মোবাইলে ঘরে বসে  একুশে বইমেলাতে প্রকাশিত বিভিন্ন লেখকের বই ফ্রী পরতে এখনই  Download করুন “Boimela 21” মোবাইল Apps. Google Play Store এ Boimela 21 লিখে সার্চ করুন  অথবা নীচের লিংকটিতে ক্লিক করুন।  https://play.google.com/store/apps/details?id=com.mahfuz.bookfair th,0,celebrity
আরো অনেক জাফর ইকবাল প্রয়োজন এই অমানুষগুলোকে মানুষ করতে। দিন দিন একটা প্রতিক্রিয়াশীল রাষ্ট্রে পরিণত হয়েছি আমরা।,0,celebrity
ভোট ডাকাত ও ব্যাংকডাকাতের বুদ্বিজীবীর চক্ষুলজ্জাও নাই,0,celebrity
পোলাপাইন কি পরিমাণ বাঁশ দিচ্ছে জাফর ষাড়রে😂😂😂😂,0,celebrity
"আমরা জানি জাফর ইকবাল সাহেবের কোন ফেসবুক আইডি নাই, উনি নিজে বলেছেন।  এইডা কোত্তে???",0,celebrity
"আসলে নারী অধিকার প্রতিষ্ঠা খুব দরকার যা কোরআন  সর্বোচ্চ মাত্রায় দিয়েছে। সমস্য হচ্ছেঃ আপনাদের দৃষ্টি নারীর প্রতি শুধু কামভাব চরিতার্থ আর ভোগের জন্য। এই জন্যে নারী অধিকার নিয়ে আপনি/আপনারা কথা বলতে পারেন না স্যার। কারণ, আপনারা নারীকে কেবলই পুরুষের ভোগ্যপণ্য উচ্ছিষ্ট দাসী হিসেবেই সমাজে প্রতিষ্ঠিত করতে চান। বাইরে যা সবই নেকামি ভণ্ডামি। ইতিহাস, প্রমাণ তা'ই বলে স্যার।   গর্তে প্রবেশের পূর্বে আমার কমেন্ট খানার যুক্তিখণ্ডন করিয়া উত্তর দিয়া বাধিত করিবেন স্যার প্লিজ।",0,celebrity
এত পড়ার ধৈর্য্য নাই কি বলে বেকুব টা।নিজে পালিয়ে পালিয়ে ঘুরে মুক্তিযুদ্ধ দেখেছে!আচ্ছা আমারা যখন সেলুনে দাড়ি অথবা চুল কাটতে যাই সাথে কে যায় যুবক বয়সে অবশ্যই বন্ধু। তাহলে কি দাড়ালো সেলুনে দুই রাজাকার চুল কাটতে গেছিলো।,0,celebrity
গায়েবানা জানাজার পরে উনি উদয় হলেন... 😒,0,celebrity
ও আল্লাহ্‌ !! ছারে দেহি বাইচ্চা আছে !!! পোলাপানগুলা তো গায়েবানা জানাজা পইরা শ্যাষ !!!!,0,celebrity
"আজ সাস্ট বন্ধ হলো ছাত্র রাজনীতির গ্যাড়াকলে পড়ে। আশা করছি, এটা নিয়েও লিখবেন স্যার :-)",0,celebrity
সার গর্ত থেকে উকিঁ দিছে😂,0,celebrity
দ্রুত সুস্থ হয়ে উঠুন স্যার। আপনি আমাদের আলোকবর্তিকা।,0,celebrity
জানাযাটা মনে হয় আর হলো না.,0,celebrity
নীতি আর বিবেক বোধকে যে আপনি বা আপনারা গণধর্ষণ করলেন তার কি হবে সার ???,0,celebrity
এইসব বালছাল  না লিখে সায়েন্স ফিকশনই লিখুন৷ সবাইরে সব জায়গায় ভাল্লাগে না৷,0,celebrity
"জি স্যার!ঠিক বলছেন,খবরের কাগজ দেখতে সাহস পান না আপনি।পাবেন কিভাবে বলেন স্যার?আপনি যে মুক্তিযুদ্ধে যেতেই সাহস পান নি।আর আপনি যে পুরনো পত্রিকা পড়েন তাও তো জানা ছিলনা।আজকের পত্রিকা ৩/৪দিন পরে আপনি হাতে পান।হায় আফসোস।",0,celebrity
"আপনি নিজেও একজন সুবিধাবাদীগোচের লোক তাই প্রমাণ দিলেন। কোটা হারানো আপনাদের কাছে স্বর্গ হারানোর চেয়ে ভয়ঙ্কর। আপনি একটা শব্দকে নিয়ে  অনেক ফিরিস্তি দিয়েছেন কিন্তু এর মূল হোতা সম্বন্ধে কিচ্ছু বললেন না। একেক শব্দের প্রয়োগ একেক কালে বিবর্তিত হয়ে একেক রূপ নেয়। মূল কথা এর ব্যবহার কেমন তাই দেখা হয়। আপনার উপর হামলা হলে আমরা সাধারণ ছাত্রসমাজ প্রতিবাদ র্যালি বের করি। শাহবাগে আমরাই ছিলাম সংখ্যাগুরু।আর তখন আমাদের প্রশংসায়  একেবারে গদগদ,আর আজ যখন আবার আমরা এমন একটা ন্যায়ের দাবি নিয়ে  আসলাম আপনার সংকীর্ণ স্বার্থে আঘাত লাগলো বলে ফুসে উঠলেন। শুনেন একটা বৃহত্তর অংশকে বাদ দিয়ে  দেশের  উন্নতি হয় নি।  আপনাকে শ্রদ্ধা করি আশা করেছিলাম বরাবরের মতো আমাদেরকে নিয়ে পজিটিভ কিছু বলবেন, কিন্তু আপনার মুখে ও মতিয়া চৌধুরীর মত জঘন্য ভাষা বের হচ্ছে।  স্যার, নিজের জন্য আপনাদের আর কত বছর সুবিধা লাগবে? এবার দেশটার জন্য একবার ভাবুন।",0,celebrity
"রুহুর আমীন একটু দুষ্টুমি করেছে, ডেকে মাথায় হাত বুলায়ে দেন ঠিক হয়ে যাবে।",0,celebrity
"আপনাকে সালাম ... আপনার জন্য হয়তো এখনও ""মুক্তিযুদ্ধ 1971"" কলমে আসে✌✌✌",0,celebrity
জাফর ইকবালের এই ধরনের লেখা আগে কখনো পড়িনি। অবাক হলাম।।।।,0,celebrity
এই ব্যাটা কি লিখছে দেখেন   https://www.facebook.com/being.frolic/posts/727106693993205?comment_id=727473117289896&offset=0&total_comments=22,0,celebrity
"আমাদের দেশের একি করূন অবস্থা যার টাকা আছে তারাই এখনমাএ পড়াশুনা করতে পারছে।এমন হলে আমাদের দেশটা উন্নতির বদলে আরো অবনতি করবে।আর প্রশাসন কে বলে কী হবে তারাইতো এখন প্রশ্নপএ বিক্রি করছে।তারাই যদি এই কাজটা না করে তাহলে এত বড় কাজটা আর কারা করবে।প্রশ্ন ফাস হওয়ার কারণে যত আবোল তাবোল আর গাধা ছেলেমেয়ে পরীখ্খায় টিকে যাচ্ছে।আর এরাই কিনা পরে শিখ্খক হবে!যারা কিছুই পারেনা তারাই কিনা আবার অন্যদের শিখ্খাদেবে।এটা কোন ধরনের পাগলামি।আর এই জন্য আমাদের দেশটা আরো অবনতি করবে।তাই সবাইকে উদ্দেশ্য করে বলতে চাই ""আমরা যদি এখন এর বিরুদ্ধে সোচ্চার না হই তাহলে আমাদের কষ্টকরে পড়াশুনা করে লাভ নেই""।যদি পড়াশুনা করে ভাল কিছু না'ই করতে পারি তাহলে সেই পড়াশুনা করে লাভ কি।",0,celebrity
"এতকাল উটপাখির মত বালুতে নিজ মুখ গুজিয়া রাখিয়া একরাশ গভীর ঘুমের পরে মাত্র তিনার ঘুম ভাংগিয়াছে, অতঃপর তিনি এখন কিছুটা বিচলিতময় পোষ্ট দিয়া পায়ের উপর পা রাখিয়া ফুরুত ফুরুত ""চা"" চিবাইবেন আর ঢেকুর গিলিয়া নিজের দায়িত্বটা সম্পাদিত করিবেন 😊",0,celebrity
কাকু জেগে উঠেছেন । কাকু ঘুমে ছিলেন ।,0,celebrity
"""আমি রাজাকার "" এই শব্দ টা ছিল সার্কাজম।  😂 এটা যখন পবিত্র সংসদে আপনার দলের সিনিয়র কোন নেত্রির মুখ দিয়ে উচ্চারিত হয়েছিল,  তখন আপনি কোন গর্তে লুকিয়েছিলেন?",0,celebrity
wishing you ## happy birth day##,0,celebrity
"মরার পরে স্ট্যাটাস দিছেন ক্যামনে? আমি রেডিওতে আপনার জানাজা দেখে খুবই কস্ট পাইসিলাম, একজন শিক্ষাবিদ এভাবে মরে যাবে আন্দোলনে অংশ না নিয়ে ভাবতেই কেমন লাগে। কিন্তু আপনি মৃত্যুকে ভুল পমান করে জেগে উঠেছেন, স্যালুট আপনাকে স্যার।  ""ওয়েকলাম টু আর্থ ব্রো"" 🌸",0,celebrity
স্যার মনে হয় এটা ঘুমে লিখেছে না হয় মদ খেয়ে‌ 😜😜  এজন্য গুজব বলে উড়িয়ে দিলুম 😜😜😜,0,celebrity
আইএম প্রাউড অফ মাই ষ্যাঁর!,0,celebrity
স্যার নাকি আজ চেতনায় বুদ হয়ে।চেতনাকর্মীদের কর্মকান্ডে চুপ হয়ে আছেন? আজ আর স্যারের বমি করতে মন চায় নাহ।স্যার এই চেতনাকর্মীদের অপকর্ম দেখে নারীবাদী কথা আওডান পারবেন নাকি দালালী করে যাবেন।,0,celebrity
চেতনাবাজ বুদ্ধিজীবী!,0,celebrity
স্যার আপ্নে দালাল সেটা প্রমাণিত। আপনার অটোগ্রাফ দেয়া টিশার্ট টা ভাবতিছি পুড়ায়া ফেলবো : ),0,celebrity
আপনি বেচেঁ আছেন 😱😱😱😱 আপনি না মারা গেলেন  শিশু কিশোর এর বই চোদাও আর হালার পু এখন গুমায় মনে কইতাছে রে কোয়েল পাখির ডিম গুলা চেইচ্চা দেই😡😡,0,celebrity
"স্যার সিলেটে বাতাবী লেবুর চাষ কেমন হয়? একটু যদি বলতেন দয়া করে..😞  অনেকক্ষণ বিটিভি দেখলাম কিন্তু ওরা দিনাজপুরের লেবুর খবর দিচ্ছে, সিলেটের বাতাবী লেবু চাষের খবর জানা খুব দরকার।",0,celebrity
শুনছিলাম জিন্দা মানুসের জানাযা পড়লে নাকি মানুসটা সত্যি সত্যি মইরা যায় ৷ সার কি এসবে বিশ্বাস করেন? সারের গায়েবানা যানাযা একটা ইভেন্ট খোলা হইছে ইতিমধ্যে প্রায় চল্লিশ হাজার লোক নামাযে অংশ গ্রহণের ইচ্ছা প্রকাশ করেছে ৷,0,celebrity
"অনেকদিন পর মনে হলো সপ্ন কখনো হারায় না, কারণ সপ্ন দেখানো মানুষগুলো তা হারাতে দেয় না.....😊😊",0,celebrity
কোদাল 😂😂,0,celebrity
ছাত্রসমাজকে ফুসলিয়ে কাম নাই ✌এরা মজুরী ছাড়াই শ্রম দিবে ✌ রাজপথে আপনার মতো দুর্বল মানুষের প্রয়োজন ওদের নেই✌ আল্লাহ আল্লাহ করেন ✌,0,celebrity
আমার বমি আসতেছে। ইচ্ছা করতেছে আপনার উপর কিছুক্ষন হর হর করে বমি করি।   এই কমেন্ট পড়ে যার চুলকাবে ওর বাপ তিনটা। 😒,0,celebrity
সুন্দর তথ্য ও উদাহরণ দিয়ে আমাকে সহযোগিতা করায় স্যারকে ধন্যবাদ।,0,celebrity
পোস্টে কি লিখেছন পড়িনি কমেন্ট পড়তে আসলাম। আমার হড় হড় করে বমি পাচ্ছে।,0,celebrity
ছ্যার আমী কীণ্থূ  ষুধ্ব ভাংলায খমেন্ত খইরথাছি😝 ভীগ্গান বীত্থীখ খমেন্ত আমী লিকভার ফারী ণা। খমা শুনধর ধৃশ্ঠিথে ধেখবেন,0,celebrity
হাতুড়িই' বাংলাদেশ... জাফরের মোচই বাংলাদেশ।,0,celebrity
এরা সবাই মুকশ পরা বাকশাল হায়েনা 😡,0,celebrity
"১০ বছর ক্ষমতায় থেকে ১২ বছরের পুরাতন জাবর কাটেন, লজ্জা করেনা আপনাদের?  জনপ্রিয়তার উচ্চ আসন থেকে কোন নর্দমায় নেমে এসেছেন ছদ্দবেশ নিয়ে হলেও যাচাই করবেন",0,celebrity
"Sir, মেলায় আসবেন নাকি আজ?",0,celebrity
জাতি আর স্যারের লেখা আগ্রহ নিয়ে পড়ে না । শুধু কমেন্টস পড়ার জন্যই এদিকে আসে,0,celebrity
দাদাভাই মরে নাই 😍 আহ দাদা WTF কেউ আবার অন্য কিছু ভাব্বেন না 😑,0,celebrity
"একি মায়ের দুই সন্তান। একটা জাত, আরেকটা কু-জাত কেমনে হয় তার উদাহরণ আপনি আর শ্রদ্ধেয় হুমায়ুন স্যার 👹",0,celebrity
কেউ কমেড খেয়ে গাঁজা দিপেন না😛😛😛,0,celebrity
কমেন্ট পড়লেই বুঝতে পারবেন স্যার আপনার অবস্থান কত নিচে নামছে।,0,celebrity
কলম থামানো যায় না কখনওই,0,celebrity
মৃত্যুর ভূয়া খবর বের হওয়ার পর স্যার জেগে উঠেছে। :D,0,celebrity
কমেন্ট পড়ো Sultana Pranty,0,celebrity
সরকারের পক্ষে বললে আওয়ামী দালাল।বিএনপির পক্ষে বললে পাকি দালাল।মুক্তচিন্তায় বললে নাস্তিক।এসব তো এখন আসলেই ট্রেডিশন মাত্র।মূলত আমরা কেহই নিরপেক্ষ না।মানুষ কখনও নিরপেক্ষ হয় না।হতে পারে না।যার যার জায়গা থেকে যার যার মন্তব্য থেকে প্রমাণ করে সে কতবড় অপদার্থ আর দেশের জন্য অপ্রয়োজনীয়।আর কত প্রেম ভালোবাসার অতীত টেনে কান্না কাটি আর স্যাড সঙ শুনবে মানুষ! ধর্ষণের ইতিহাস ইয়াসমিন থেকে শুরু করেন গুগোল করেন।লজ্জায় মরে যাবেন... আপনার লেখা পড়ুন।আপনি একজনকে নিয়ে তামাশা করেন অন্য রা আপনাকে নিয়ে করে।তবে হয়তো যৌক্তিক।উপরে থুথু মারলে উপরে যায় না নিচেও যায় না পাশেও যায় না-মুখেই পড়ে।,0,celebrity
আর কত? আর কত কাল এসব সহ্য করতে হবে। গত রাতেও টিভিতে ভিকারুননিসা নুন স্কুলের এক শিক্ষক বললেন বোর্ড থেকে এবং শিক্ষামন্ত্রানালয় থেকে নির্দেশ দেয়া হয়েছে বানান ভুল হলে কিংবা বাক্য গঠনে ভুল হলে কোন নাম্বার কাটা যাবেনা। ২৫ নম্বর পেলেও তাকে পাশ করিয়ে দিতে হবে। প্রতিনিয়ত প্রশ্নপত্র ফাস হচ্ছে আর সরকার বড় বড় কথা বলছে। আবার বিশ্ববিদ্যালয়ের ভর্তি পরীক্ষায় পাশ করতে না পারলে বিশ্ববিদ্যালয়গুলোর দোষ দেয়া হচ্ছে। এরকম শিক্ষার কি কোন দরকার আছে? আগে মানুষ ফোনে বা  বিভিন্ন ভাবে প্রশ্ন পত্র খুজতো। আর এখন প্রশ্ন পত্র নিজেই বাসায় এসে উকি দেয় আর বলে এই আমাকে লাগবেনা তোমার? নিষ্পাপ শিশুদের আমরা আর কত ভাবে যন্ত্রনা দেব? আর কত ওদের ক্রিমিনাল বানানো হবে। এক দুজন মানুষ আমরা ওদের বিরুদ্ধে কথা বলে কি লাভ? ওরা যা করবে তাতো করেই যাবে। ধিক এই শিক্ষাব্যাবস্থার উপরে বসে যারা কলকাঠি নাড়াচ্ছেন তাদের শুভবুদ্ধির উদয় হোক।,0,celebrity
ঝ্রাফিবাল কী এখনো বেচে আছে?? কালকে না গায়েবী জানাজা পড়লাম😎 তই এডমিন কথা গুলা কিরাম লাগল 😂,0,celebrity
"মদ খা শালার পুত!! মদ না খেলে তোর বুদ্ধি বাড়বে না, মানুষ হবি না!!",0,celebrity
"সময়োচিত লেখা,ধন্যবাদ প্রিয় স্যার... ♥",0,celebrity
বদ্ধ উন্মাদ একজন মেধাবী যিনি সাইন্স ফিকশন লিখেন কিন্তু ফেইসবুক লাইভ কি বুঝেন না। আবার সমালোচনা করতেছেন কিন্ত  পুরো বিষয়বস্তু জানেন না... আসলেই আমি ঘাস খাই,0,celebrity
আন্দোলনের সময় একটা ট্রাক এক বাচ্চার উপরে তুলে দিলো কেন?  জাফর স্যার জবাব দ্যান?,0,celebrity
"আপনি আমাদের বাংলাদেশের গর্ব স্যার, শুভ জন্ম দিন।।",0,celebrity
আমারও উপন্যাসটা বেশি ভালো লেগেছে:),0,celebrity
"আপনার লেখার প্রথমে দেখলাম বিশবিদ্যালয়ে ভূর্তির ব্যাপারে কি জেনো বললেন। বিশবিদ্যালয়ে ভূর্তির যদি এস এস সি এবং এইছ এস সি ফলাফলের উপর নির্ভর করে দেয়। তাহলে গ্রামের ছাএ ছাএরা কথায় পরবে। কেননা গ্রামের চেয়ে শহরে পড়া লেখা মান ভালো। গ্রামের ছাএ ছাএরা অনেক মেধাবী কিন্তু তারা ভালো শিক্ষক, পরিবেশ না থাকার কারনে তারা ভালো ফলাফল করতে পারে না। কিন্তু  তারা শহরের ছাএ থেকে অনেক মেধাবী তা ভূর্তি পরীক্ষার মাধ্যমে প্রমান হয়। এখন সরকার এস এস সি ও এইছ এস সি পরীক্ষায় তো মেধা যাছাই করে না বিশবিদ্যালয়ে ও করবেন না। আমরা এর প্রতিবাদ করি।",0,celebrity
"স্যার ৯১ থেকে ৯৫ এর সময়ে আপনার একটা লিখার লিংক দিতে পারবেন? 😕😕 না আপনার মুখে ""আওয়ামী-জামাত"" শুনতে চাই...৯৬ তে আওয়ামীলীগ ক্ষমতায় আসে জামায়াতের সাথে জোট করে? আপনি জানেন না? আপনি কি মুচওয়ালা টিন এজার? 🐸🐸",0,celebrity
"আপনার ছেলে মেয়ে তো বহাল তবিয়তে পিএইচডি করতেছে ,,,,,, মরছে তো সাধারন বিশ্ববিদ্যালয় স্কুলের  ছাত্র ,,,,,,,,  এমন নির্বাক চুপ থাকাটা কি "" ডিজিটাল রাজাকারের "" পর্যায়ে পড়ে যায়না ??",0,celebrity
আমি স্যারের দারুন ভক্ত। উনার লেখা বাধ্য করে বই এর বাজারে যেতে। লেখা বিক্রেতা হিসেবে বাড়ীর  শিশুদের  মাসিক বাজেট কে যেভাবে প্রভাবিত করতে পেরেছেন তা রাজনিতীর বাজারে বড়দের বেলায় অতটা সহজ না বোঝা যাচ্ছে।তাই বলি থাকুন না টিভি রুম চিপস আইসক্রিম নিয়ে কি দরকার বড়দের মাঝে আসার।,0,celebrity
উনি কি সদ্য কবর থেকে উঠে আসলেন? পাবলিকতো ওনার গায়েবানা জানাজা আদায় করে ফেলেছে? 😂😂😂😂,0,celebrity
"সবাই দেখি কমেন্টস করছে,ভাইয়ারা এখন একটু দয়া করে আনলাইক করে দেন পেইজ টা......এই সব দালাল লোকদের পেইজ এত লাইক...!???",0,celebrity
অভিজিতের লেখাও পড়েছি আবার বই ও পড়েছি ।সে নিজে এক লাইন ভূমিকা লিখে বাকিটা কোথাও না কোথাও থেকে কপি করে দেয় আর শেষে রেফারেন্স দেয় । আর এর লেখা দেথেই আপনি অবাক ।,0,celebrity
অনলি তৈলল ইজ রিয়েল।,0,celebrity
স্যার আপনার মুখে মুক্তিযুদ্ধ আর কোটার কথা শুনলেই কেমন হড়হড় করে বমি করতে ইচ্ছে করে। আর আপনিওযে যুদ্ধের সময় গর্তে লুকিয়ে ছিলেন সেটা আমরা জানি।যেমন লুকিয়েছে ৭১ পরবর্তী রাজাকাররা। অতএব ৭১এর পরে জীবন ভয়ে গর্তে লুকানো=রাজাকার। ৭১ এ ভয়ে জীবন ভয়ে গর্তে লুকানো। দুইটাইতো রাজাকার তাইনা স্যার?,0,celebrity
"লেখাটা পড়ে খুব ভাল লাগলো, সমার্বতনে থাকতে না পারা কষ্ট কিছুটা হলেও কমে গেছে। আর আসলেই আমাদের দেশটা চাষী, নারী এবং অন্যান্য সাধারণ জনগণের জন্যই এগিয়ে যাচ্ছে। আমরা শিক্ষিত ব্যক্তিরা যদি সত্যিকারের দেশকে ভালবাসতে পারি তবেই চতুর্থ পিলার হিসাবে দেশের কাজে লাগতে পারব অন্যথায় সম্ভব নয়।",0,celebrity
অবশেষে দানবের বোধ জেগেছ্।,0,celebrity
"১৯ বছরের সমায় যে যুদ্ধ না করে গর্তে বসবাস করে সেই রাজাকারের মুখে তালিম ভাল শুনায় না, হালায় একটা রাজাকার।।",0,celebrity
আমি হূমায়ুন আহমেদের ভাই বলে এই লোককে এ পর্যন্ত তেমন কিছু বলি নাই।,0,celebrity
"অভিজিৎ আপনার স্যারের ছেলে,  তার বিচার চাইলেন, যে দেশে বিশ্বজিত হত্যার ভিডিও ফুটেজ আর কোন অপরাধ না থাকা হত্যার বিচার হয়নি,  তবে অভিজিৎ এর কোনো দরকার ছিলো না আমার ধর্ম নিয়ে লেখার,কারণ মুসলমান ধর্ম একটি প্রতিস্ঠিত ধর্ম,মুসলমান ধর্মের কিছু পরিবর্তন বা পরিবর্ধন করার জন্য আলেম সমাজ আছে,  তোমার মতো ডান্ডির বাচ্চার সেটা নিয়ে চিন্তা না করাটা ভালোই ছিলো",0,celebrity
যুগে যুগে জাফর।।।।। মীর জাফররাই আসে।।।,0,celebrity
লেখা পড়ি নাই! কেবল কমেন্ট গুলো পড়তেছি আর আপনার চামড়া কতো মোটা সেটা ভাবতেছি😞,0,celebrity
আসলে স্যার আপনাদের মত লোক এখনও আমাদের দেশে আছে বলে আমাদের দেশটা এখনও বেছঁ আছে,0,celebrity
মুছুওয়ালা শয়তান টা কি প্রতিদিনের গুম খুন চোখে দেখে না?,0,celebrity
অদ্ভুত!,0,celebrity
আসাধারণ স্যার। সত্যি আপনাকে স্যালুট,0,celebrity
এই পোস্টটা বিদেশি কোন লেখকের কাছ থেকে চুরি করা নয়তো আবার?? 😂,0,celebrity
"স্যার,আপনাকে অনেক ভালবাসি।",0,celebrity
উহাদেরকে বলা হয় জ্ঞান পাপী। জ্ঞান বেড়ে গেলে মানুষ পাগল নয়তো উন্মাদ হয়ে যায়। ওই সয়তানের খেত্রে তাই হয়েছে।,0,celebrity
আপনেরা বুঝেন না কেরে? হেতে তো হেতার নামধাম ভুলি গেছে।,0,celebrity
স্যার আগে আপনার বই পড়তাম।আপনার অনেক বড় ফ্যান ছিলাম।😍😍  কেন ছিলাম?😑😑😐,0,celebrity
"কমেন্ট পড়তে পড়তে রাত শেষ হবে, উপরের মূল্যবান লেখাটি পড়ব কখন? 😢",0,celebrity
আগাছা একটা,0,celebrity
আমাকে কি স্যারের Email Address টা কেউ দিতে পারবেন?,0,celebrity
ব্রাদার্স ষ্যারের পোষ্ট এ এতো হাহা রিয়াক্ট কেনো 🐸🐸,0,celebrity
"স্যার , টানা কয়েকদিনের প্রবল বর্ষনে মনে  হয় আপনার গর্তে পানি জমে গেছে,তাই  শেষ মুহূর্তে ছোট গল্প লেখার জন্য গর্ত নিদ্রা ত্যাগ করে  বের হলেন।তাই নিজের দায় আর পাপ    মোচন করতে আসছেন।মনে কলুষতা, দালালি রেখে, গঙ্গায়  স্নান করলে কি কাজ হবে???",0,celebrity
আপনাকে একটা অনুরোধ আপনার নাম থেকে মুহাম্মদ বাদ দেন । ok,0,celebrity
আর কত ম্যান!  আপনি এবার থামেন।আপনি কথা কইলেই মুখ থেকে বমির দুর্গন্ধ আসে।অনেক বমি করছেন জীবনে।পুরা দেশটাকে বমি কইরা ভাসায় ফেলছেন।এবার মুক্তিদেন দেশের মানুষকে আপনার দূর্গন্ধ থেকে।,0,celebrity
"সাড় চল চন্দ্রিমা উদ্যানে যায়,,, ঘাস গুলো কাটার মেশিন নষ্ট,,",0,celebrity
"Muhammed Zafar Iqbal স্যার, মানুষ যখন নিজের জন্য লড়াই করে-সেটা বাঁচার জন্য লড়াই। আর মানুষ যখন দেশের জন্য লড়াই করে সেটা-বাঁচানোর জন্য লড়াই। সে লড়াইয়ে নিজের প্রানের মায়া থেকে অন্যের প্রান বাঁচানোর মায়া বড় হয়ে যায়। যারা এত এত মায়া দিয়ে আমাদের বাঁচানোর জন্য লড়াই করলো তাদের জন্য আমর কি করলাম??? তাদের সন্মানটুকু আমরা দিতে পারছিনা!!!  বড় কষ্ট নিয়ে বলছি স্যার, আমরা শুধু বাঁচার জন্যই লড়ছি-বাঁচানোর জন্য লড়াই করার মনোবল আমাদের নেই। আমরা আজ স্বার্থপর-লজ্জাহীন।।।",0,celebrity
স্যার সম্মিলিত ভর্তি পরীক্ষার কি অবস্থা?! ওটা হবেনা?,0,celebrity
স্যার আপনাকে উইকিপিডিয়ায় মৃত দেখাচ্ছে কেন??,0,celebrity
ঘুরে ফিরে আবার সেই 'রাজাকার' ইস্যু। নতুন কিছু পান না? এত জ্ঞানী একটা মানুষ আপনি সার্কাজম বোঝেন না কিভাবে? নাকি বুঝেও এরকম আচরণ করেন?,0,celebrity
আমি জানি না আপনার বয়স কত আমি নিশ্চিন্তে বলবো আপনি এক জন আ...মী...গ আপনি যে কথা গুলি লেখেচেন তাতে বুঝা যায় আপনি বোকা বোকা বোকা,0,celebrity
কন্ডমের প্যাকেট এর মতো তেলতেলা মনে হচ্ছে এই লেখাটি Abrar Ahmed Rafi,0,celebrity
আমরা আছি আপনার সাথে.........,0,celebrity
আমি সরকার বা বিরোধী দল বুঝিনা। আমি বুঝি আমরা হেরে যাচ্ছি আমাদের সময়ের কাছে। আমরা পা না ঢেকে পৃথিবী ঢাকার চিন্তা করি। হরতালেও পরীক্ষা চলুক। ক্ষতি জমে জমে ভবিষ্যতের লাভ হোক!,0,celebrity
"Didarul Alam আমরা ভাল নেই। আজ একাত্তরের হায়নাদের সহযোগী জামাত, বিএনপির জোরে ও বিগত ৩৫ বছরের উপার্জিত অবৈধ অর্থের জোরে তান্ডব চালাচ্ছে। জনগনের নিরাপত্তা বিধানে পুলিশকে অসহায় মনে হচ্ছে। জবাই করে জামাত শিবিরের কুত্তারা রাজিবকে মারল, মারল আইনশৃঙ্খলায় ও জনগনের জানমাল নিরাপত্তায় নিয়োজিত রাস্ট্রযন্ত্রের সশস্র বাহিনীকে আর তখন খালেদা এই জঙ্গীদলকে সমর্থন দিয়ে হরতাল ডাকছে। বলছে সরকার নাকি গনহত্যা চালাচ্ছে! যারা গনহত্যা করেছিল তাঁদের বাঁচাতে খালেদা পারবে কি? জনগনকে আর কতদিন ধোকা দিবে সেই মীরজাফর জিয়ার স্ত্রী আর তার সাথে মুক্তিযোদ্ধা নামধারী মীর্জাগংরা! আজ কক্সবাজারে সন্ধায় নরপিশাচরা চোরাগুপ্তা মিছিল বের করে তান্ডব চালানোর চেস্টা করল। শুধুমাত্র পুলিশের হামলায় ছত্রভংগ হল। কয়েক হাজার পর্যটক আটকা পড়ে আছে এই নরপিশাচ আর পাকি দালালদের হীন স্বার্থ চরিতার্থ করার কারনে! তাই বলছিলাম ভাল নেই, মনে হয় একাত্তরের মত আবার যুদ্ধ শুরু করতে হবে ছাত্র-জনতা-আবাল-বৃদ্ধ-বনিতাকে! তাছাড়া উপায় কি বলুন? সরকারের আরও কঠিন হাতে দমনের পরিকল্পনা না থাকলে খালেদ-গংগরা সুযোগ নিবেই। খালেদা একাত্তরের গনহত্যা চিনেনা, জামাত-শিবিরের জঙ্গি ততপরতা, ভাংচুর, খুন, জালাও পোড়াও চোখে দেখে না! এখন আমাদের একশানে যাওয়া ছাড়া মনে হয় আর শেষ রক্ষা হবে না। পতাকা পোড়াচ্ছে, সঙ্খ্যালগুদের খুন করছে ঘরবাড়ি পোড়াচ্ছে, সম্পদ লুট করছে! পুলিশ অসহায়! তাই সবাইকে আহ্বান জানাচ্ছি, আসুন ঘরে ঘরে প্রতিরোধ গড়ে তুলুন। সেই একই স্বাধীনতাবিরোধী শক্তিকে রুখে দেই। এবার অন্তত পাকিস্তান বাহিনী অদের বাঁচাতে আসবে না, আসবে তাঁদের প্রেতাত্মা (খালেদা-মির্জা গংরা)। জয় বাংলা। একাত্তরের হাতিয়ার, গর্জে ঊঠুক আর একবার। আমাদের স্বাধীন সোনার বাংলাকে আর কেঊ ধর্সন করতে পারবে না, আমরা তা মেনে নিব না। ওদের সমুলে ধ্বংস করার এখনই সময়। জাগো বাঙ্গালী জাগো।",0,celebrity
"কে যেন ফেসবুকে প্রচার করেছিল আপনি আর ইহজগতে নেই! আমি বিশ্বাস করিনি। স্যার মরতে পারেন না। আমার ধারনা সত্যি হল। স্যার ছিলেন, আছেন, থাকবেন, লিখবেন, নাচবেন, গাইবেন, জাতিকে উদ্ধার করবেন।",0,celebrity
ধর্মকে টেনে আনাটা ভালো হয় নাই।,0,celebrity
ধন্যবাদ স্যার। ভালো থাকুন সবসময়।,0,celebrity
স্যার আপনি বর্তমানে এত বুদ্ধিতে জীবিত আছেন যে আপনার হিতাহিত জ্ঞান লোপ পেয়েছে। আপনি আমাদের সেফুদার সরনাপন্ন হতে পারেন।এতে করে হতে পারে এই বয়সে এসেও কিছুটা বুদ্ধিলোপ পেয়ে একটু হিতাহিত জ্ঞানটা বৃদ্ধি পাবে।👴👉👵👉👶😷😷,0,celebrity
Question তো ফাঁস হয় আবার এর সাথে কিছু busterd teacher[এই  ধরণের শিক্ষকদের কী বলব তার ভাষা আমার কাছে নাই] আছে যারা পরীক্ষা রুমের ভিতরে গিয়ে ছাত্রদের কে Answer sheet দিয়ে দেয়,0,celebrity
You are r8 sir and we want peace at any cost... Thnq so much sir....,0,celebrity
এই ব্যাপারে জাফর ইকবাল স্যার এর ব্যাখ্যা আশা করছি  http://istishon.com/node/7927,0,celebrity
মৃত মানুষ হয়ে ও আপনি কিভাবে এইসব লিখলেন ষ্যাঁর? তাহলে কি আপনি স্বর্গে বসে এইসব লিখতেছেন? বিদায় পিতিবী😂😂😂,0,celebrity
আত্বঘাতী মন্তব্যের জন্যে যথোপযুক্ত উত্তর প্রদান করেছেন স্যর।ধন্যবাদ,0,celebrity
ekta jinis buji na....দেশটা তো আমাদের।  শুধু দুইটা মানুষের কথায় দেশ চলতে পারে না...,0,celebrity
"আপনি যদি ফ্রিলান্সিং / আউট সোর্সিং সম্পর্কে আগ্রহী হন তাহলে আপনার জন্য পেইজটি ভালো ভূমিকা পালন করবে। কোন কিছু জানার থাকলে পেজের পোস্ট করুন অথবা মেসেজ করুন, সেই সাথে কমেন্ট বক্স তো আছেই। https://www.facebook.com/OutsourcingHelpLine",0,celebrity
আসুন হাহা দিয়ে বিশ্ব রেকর্ড করি।,0,celebrity
Yes sir we r marching on.no one's gonna stop us.amra jitboi..amra dekhiye dbo kono kisutei amra voy paina jemnta paini 71 e:),0,celebrity
"আমাদের শিশুদের লেখাপড়ার দরকার নেই,দোহাই আপনাদের, তাদের ক্রিমিনাল করে বড়করবেন না!",0,celebrity
"আর কত দিন এইভাবে চলবে...??? ১০০ জন পরীক্ষার্থির ভেতরে ৭০ জন পাশ করবে, কিন্তু এই ৭০ জনই যেন সুশিক্ষিত হতে পারে তার ব্যবস্থ্যা করতে হবে। ৫ম শ্রেণীতেই দূর্ণীতি শিখে বড় হচ্ছে, তাইলে ভবিষ্যতে ঘুষখোর সরকারি কর্মচারী হওয়াটাই সাভাবিক :( দিন-দিন আমরা সামনের দিকে না এগিয়ে আরো পিছিয়েই যাচ্ছি...... :(   https://www.facebook.com/video.php?v=10152867349604644&set=vb.13678589643&type=2&theater",0,celebrity
ক‌মেন্ট পড়‌তে অাসলাম 😄😄,0,celebrity
" পরীক্ষা তো দিসি, তাই বলতে পারি ফিজিক্স ফাস না হলে কোনো বোর্ডে ৫০ ভাগ পাশ করতো কিনা সন্দেহ। বেশি বুজছিলাম তো তাই BUET কে টা টা দিতে হল।",0,celebrity
উয়ায়ায়ায়ায়ায়াক্ক উয়ায়ায়ায়ায়ায়ায়ায়াক্কক্কক্ক উয়ায়ায়ায়ায়ায়ায়ায়ায়ায়াক্কক্ক আমি শেষ।,0,celebrity
যাক চাপের মুখে মুখ খুল্লেন 😰,0,celebrity
"ভাবতেই কষ্ট হচ্ছে এতদিন আমি একটা ভুল মানুষকে ভালো এবং মহৎ মানুষ হিসেবে ভেবে এসেছি। আমাদের দেশটা বুদ্ধিহীন হয়ে গিয়েছিল ১৪ই ডিসেম্বর রাতেই। আর রেখে গিয়েছিল আপনাদের মত কিছু সুবিধাবাদী মানুষকে যারা স্বাধীনতার এতটা বছর পরেও দেশের প্রকৃত উন্নয়নের জন্য কিছু করতে পারেননি। ''আমাদের দেশে হবে সেই ছেলে কবে, কথায় না বড় হয়ে কাজে বড় হবে'' এটা মনে হয় আপনার মত মানুষের কথা ভেবেই লিখা।",0,celebrity
"হারামীটা ৫ দিন পালস দেখল, প্রধান্মন্তত্রি কি বলে দেখল, তারপর সেই হিসেবে হরহর করে বমি করতে আসছে..",0,celebrity
"অর্ধেক পড়েছি,,",0,celebrity
লেখাটি অনেক সুন্দর হয়েছে,0,celebrity
কাঠাল পাতা প্রয়োজন।,0,celebrity
সে মাঝে মধ্যে খবর পড়তে ভয় পেয়ে যায়। হঠাৎ ভয় পেয়ে চিৎকার করে উঠে।চোখ বন্ধ করে ফেলে।পরে অজ্ঞান হয়ে গেলে আস্তে আস্তে সাহস করে একটু একটু করে পড়ে। আহারে হৃদয়বানরে... আহারে ভন্ড... দুধের বাচ্ছাদের বুঝাচ্ছে...!,0,celebrity
এসব চ্যাটের কথা বলে জনগণের মন তো দূরের কথা দেহও পাবেননা জনাব চ্যাটিকবাল সাহেব :(,0,celebrity
সব দিক দিয়ে লেখাটা অনেক সুন্দর,0,celebrity
"আমরা তাদেরকে সত্য এবং ন্যায়ের কথা বলি, কিন্তু অসত্য আর অন্যায়কে লালন করি– এত বড় ভণ্ডামির উদাহরণ কি আর কেউ দিতে পারবে?",0,celebrity
লেখা লিখিরও দরকার ছিল না। একটা দিন বাচ্চা গুলোর পাশে দাড়াতেন ওদের  সাহস হাজার গুন বেড়ে যেত। কোথায় আপনি?,0,celebrity
স্যার আপনি তাহলে বেচে আছেন???,0,celebrity
আপনার আসল চেহারা বাংগালি দেখে ফেলেছে।,0,celebrity
গায়েবী জানাজা আর পড়া লাগবে না,0,celebrity
ঠ্যালা তাহলে এখানেও  লাগছে  মৃত মানুষ জীবিত হয়ে গেলেন  ঠ্যালার নাম বাবাজি,0,celebrity
"আচ্ছা, বাংলাদেশের নাম বিদেশিরা বেংলাডাস বলে কেন?এ বিষয়ে কিছু লিখেন। আর হ্যা,আপনার পোস্ট পড়ে সবাই এতো বমি করে কেন?",0,celebrity
"আপার প্রতিটি কথাই এক একটি বই। এবং সবাই  আপনাদের মত করে মাকে ভালোবাসুক ও সমম্যান করুক, তা হলে পৃথিবিতে বৃধ্যাআসরম লাগবেনা। রতন্য হয়ত অনেক আছে কিনতু  সনতানের এখন খুব আভাব, সার। আললাহ আপনাদের ভাল রাখুন,।।।  অপু",0,celebrity
স্যার আম্নের গুণগান সবার মুখে শুনে আমি হড়হড় করে বমি করে দিলাম,0,celebrity
আপনি ক্ষমতা অধিকাররে কথা নাই বা বলুন জনাব আপনার মুখে সেটা বেমানান।,0,celebrity
দেখ Lutfun Nahar Lata,0,celebrity
ষাড়😱,0,celebrity
আপনার নামতো BTV Iqbal হওয়া দরকার ছিলো দুইটিই কাজের সময় খবর থাকেনা,0,celebrity
তিনি বেঁচে আছেন??,0,celebrity
কমেন্ট পড়তে আইসা ত পুরাই টাস্কি খাইয়া গেলাম।সব ই আমার ভাই বোনেরা।কার টা রাইখা কারটা যে পড়ি।আমি টোটালি কনফিউজড :(,0,celebrity
"আশা করি আপনি শুয়রগুলার কমেন্ট পড়বেননা, আমরা পাল্টাবোনা কারণ পুনের মানুষের ভিতরে হয়তো অল্প শুয়োর আছে কিন্তু এখানে শুয়োরের ভিতরে অল্প মানুষের বসাবাস",0,celebrity
"আপনার মধ্যে তো কোন পরিবর্তন দেখছি না, স্যার। কোটা সংস্কার আন্দোলনের সময় থেকে একই বুঝ নিয়ে বসে আছেন, যেই লাউ সেই কদু।  সার্বজনীন হবার চেস্টা করুন স্যার।",0,celebrity
"স্যারের এই লেখায় বঙ্গবন্ধু,বঙ্গবন্ধুর কন্যা,মুক্তিযোদ্ধের কথিত সপক্ষ দলকে তৈল মর্দন মুলক বাক্য না পেয়ে হতাশ হয়েছি! লেখার শেষে অন্তত #জয় বাংলা বলবেন স্যার প্লিজ :)",0,celebrity
স্যার বিগত ১ মাস স্মার্ট ফোন না থাকার কারনে আপনার পোষ্টের কমেন্ট গুলো পড়তে পারিনি সে জন্য আমি আন্তরিকভাবে দুঃখিত 😕😕 যাই হোক এখন আর বিনোদনের অভাব হবে না,0,celebrity
মাঝে মাঝে কবর থেকেও মানুষও উঠে আসে....😱😱,0,celebrity
ভাই আর হাসতে ভালো লাগছে না। প্রায় ৪০ মিনিট কমেন্ট বক্সে ছিলাম। জাফর ষার কে মানুষ এতো ভালোবাসে কমেন্ট বক্সে না গেলে বুঝতামই না। ষার নাকি কোটা বিরোধী আন্দোলন নিয়ে কথা বলছে। কি বলেছেন সেটা যদি কারো কাছে থাকে আমাকে একটু জানানোর অনুরুধ করলাম. .......,0,celebrity
"আগে নিজের রাজাকার নানার কবরে হড়হড় করে বমি করুনযে, অথবা মমের কবরে, যেহেতু হেতেনে রাজাকারের মাইয়া আছিল",0,celebrity
অামি তো একটু অাগে অাপনার গায়েবী জানাজা পড়ে অাসলাম 😎😎,0,celebrity
"আপনার মত ঘটুরে ফালাইয়া পক্কাৎ পক্কাৎ মারা উচিত।  এইদেশে সাম্প্রদায়িক অত্যাচার হয় নাই? কিছুদিন আগে আমাদের হিন্দু মুক্তিযোদ্ধাকে ভিটে ছাড়া করছে। দিনাজপুরের সাংসদ সদস্যের অত্যাচারে প্রায় ৬০০ পরিবার চলে গেছে।   জিডিপি? উপুত করে পিছে ঢুকাবো!   নিজেই শিক্ষাব্যবস্থা ধ্বংস করছেন নিজের এক্সপেরিমেন্ট দিয়ে। নিজের সামনে কোটি শিক্ষার্থীর জীবন নষ্ট হইলো, নিজের সামনেই আপনার স্ত্রীকে শ্লীলতাহানি করলো সোনার ছেলে!!  আসলে ঘিনঘিন করে আপনার মত ছাগলের বাচ্চাকে দেখে। কেমনে সরকারের শিষ্ণ চুষেন। জীবনেও নিজেকে নিজের নজরে দেখছেন?  দেখলে বালের গান গাইতেন না। আমার বালের বুদ্ধিজীবী।  আপনার মত বালকে হাত মেরে বাথরুমেই জলাঞ্জলি দেয়া উচিত।",0,celebrity
"সুপ্রভাত  ,  কি অবস্থা , মদ খাবি বেচে থাকবি ।  ওকে ,",0,celebrity
"খুব সুন্দর লিখেছেন ।ধন্যবাদ ।আপনার একটা চরিএ এর সাথে আমার একটা দিক মিলে গেছে যে সব সময় দূবর্লটীমের প্রতি মায়া লাগে ,এটা কেন জানি অজানা কারনে আমার ক্ষেত্রেও হয় ।",0,celebrity
দুঃখিত স্যার কমেন্ট পড়তে আসতে দেরি হয়ে গেছে। চিন্তার কিছু নেই স্যার সত্যি বলতে আমি গর্তের ভিতরে ছিলাম। আর স্যার মনে হচ্ছে এই লেখাটা আগে কোথাও পড়েছিলাম!!! এইটা কি কপি পোস্ট ছিলো???,0,celebrity
"মুক্তিযুদ্ধের পর #জামাতের সাথে আওয়ামীলীগের দহরম মহরম কিন্তু কম ছিল না। আওয়ামীলীগের জোটে জামাত সামিল ছিল, তাদের জোটের হয়ে জামাত নির্বাচন করেছে,ক্ষমতায় বসেছে ।এই কথা কেন লিখতে ভুলে গেলেন জনাব তথাকথিত স্যার! দলকাঁনা হলে যা হয় আরকী!তখন ছাত্রলীগের পিটনও ম্যাসাজের মত লাগে😂।আপনি এখন একচোখা কাঁনা লোক তাই আপনি আর কথা বলেন না আপনার মুখ থেকে শুধু এখন বমির গন্ধ বের হয়।  আপনার জীবনের সবচেয়ে বড় ঘটনা মুক্তিযুদ্ধে আপনি অংশগ্রহন করেন নাই, ছিলেন গর্তে লুকিয়ে।   মুক্তিযুদ্ধের সময় আপনি ছিলেন তাগড়া জোয়ান,ইউনিভার্সিটির তাগড়া যুবক।আপনার তো লজ্জা করা উচিত। #বঙ্গবীর_কাদের_সিদ্দিকী আপনার বাবাকে তো সরাসরি রাজাকার বলেন। ( youtube ভিডিও আছে)।আপনার নানাও ছিলেন রাজাকার",0,celebrity
"এটা কোনো সুখকর নিউজ না যে স্কুল-কলেজের ছেলেরা দেশের রাস্তাঘাট ২-৩দিনে চেঞ্জ করে দিয়েছে।এটা আমাদের সিস্টেমে যে গলদ ছিল তা ধরিয়ে দিয়েছে।এটা লজ্জার ব্যাপার।কিন্তু কেউ এটাও ভাববেন না যে তাদের দিয়ে দেশ কিংবা রাস্তায় গাড়ির লাইসেন্স চেকিং এর জন্য প্রতিনিয়ত রাস্তায় পাঠাবেন।আজ বা কাল তাদের স্কুলে পাঠাবার ব্যবস্থা করেন।আমিও চাই তারা স্কুলে কিংবা কলেজে ফিরে যাক।আর তাদের জীবনের অস্বাভাবিক মৃত্যু রোধ হোক।ভবিষ্যতে তারাও এ দেশের কোনো না কোনো পজিশনে থাকবে। আমার বিশ্বাস তারা সকল অন্যায় মুছে দিয়ে, আজকের এ সিস্টেমের মত করে দেশের হাল ধরবে। নম্রতা,ভদ্রতা,পরোপকারীতা,আইনের প্রতি শ্রদ্ধা, রাষ্ট্রের প্রতি আস্থা,সততা ইত্যাদি গুণে আজকের এ ৮০% ছাত্রসমাজ।শুধু প্রতিবাদ মুখী নয়, দেশ তোমাদের থেকে  অনেক ভাল ভাল কিছু আশা করে। ইতি আমি এক #সাধারণ_ছাত্র_আরিফ",0,celebrity
"এই লেখা পড়ার ধৈর্য্য হারিয়ে ফেলেছি সেদিনই, যেদিন হারিয়েছিলেন আপনি। সরি স্যার।",0,celebrity
ইমাম উদ্দীন সুইট,0,celebrity
"একজন সাদাসিধে সংগ্রামী মায়ের সংগ্রামী ছেলে।আপনাদের দেখেই শিখুক এদেশের নতুন প্রযন্ম। আপনারা আছেন বলেই এদেশের নতুন প্রযন্ম বেচেঁ থাকার অক্সিজেন পায়,বুকে অনেক সাহস পায়,দেশের জন্য সংগ্রামী চেতনায় উদ্দীপ্ত হওয়ার সাহস পায়।আশা করছি এভাবেই উদ্দীপ্ত করে যাবেন পুরো বাংলাদেশের ১৬ কোটি হৃদয়কে। ",0,celebrity
হেঁতে কবরের থেইক্যা উইঠা আসলো কখন..?,0,celebrity
কেমন আছেন সার,0,celebrity
Zafor Iqbal my fabarite writer,0,celebrity
"কে তুমি বৎস, ধরিয়া মৎস, বেচিয়া গঞ্জে, অকুল ও কুঞ্জে, না খাইয়া তাজা, কেনো ভক্ষন করিয়াছো মেয়াদ উত্তীর্ণ গাজা 😂",0,celebrity
"সবার ভালবাসা, প্রধানমন্ত্রী সাক্ষাত ও ব্লাক বেল্ট ধারী ঘটনা শুনে চোখে জল না এসে পারে!",0,celebrity
মানুষ  আপনার নামে যে গুজব বের করছে তার বিচার কি হবে?,0,celebrity
কমেন্টগুলো পড়তে আসলাম। স্যার আপনিও আসেন।,0,celebrity
স্যার কমেন্টগুলো একটু মনোযোগ সহকারে পড়েন অার পালস্ বুজার চেষ্টা করুন। কল্পকাহিনী দিয়ে যেমন মোল্লারা ঠিকতে পারেনি মনে হয় অাপনার কল্পকাহিনী গুলো মানুষ অাগেরমত খাবে না।,0,celebrity
শিবিরের কারণে আজকে আপনি ভিসি হতে পারলেন না। আফসোস।,0,celebrity
দূর্জন বিদ্বান হলেও পরিত্যজ্য।,0,celebrity
আমার মনে হয় নকলের যুগ ই ভাল ছিল। তখন কিছু student নকল করত এবং অনেক বহিস্কার হত। এরপর ১০০% কমন পরত না। কিন্তু ফাস হওয়া প্রশ্নে ১০০% কমন পরে।,0,celebrity
স্যার গর্তে কি সাপের উপদ্রব দেখা দিয়েছিলো?,0,celebrity
থিসিস চুরি করলে তাড়াতাড়ি ডিগ্রি পাওয়া যায় ...   যা আপনি করেছেন,0,celebrity
"মেধাবীরা এসে গেছে,জাফর স্যার যথারীতি আবার নাস্তিক-মুরতাদ হয়ে যাবেন",0,celebrity
"আমার ভগবান আপনাকে দীর্ঘজীবী করুক, যাতে করে আমরা, এই পৃথিবীর সকল অধিবাসীরা প্রাণের ছোঁয়া পাই। ভালো থাকুন স্যার।",0,celebrity
"বিকৃত মানসিকতার এই জনগোষ্ঠী শুধু ধ্বংসের পথে হাটতে চায়।কারন উপরে উপরে সমস্যা জিইয়ে রেখে কোনভাবেই সমস্যার সমাধান সম্ভব নয়, সমাজের স্ট্রাকচার ই এখানে দুর্নীতিগ্রস্থ।",0,celebrity
"অন্যেরা কী করবে জানি না, কিন্তু আমি কী করব মনে মনে ঠিক করে রেখেছি। তাহলে আমি শহীদ মিনার কিংবা এরকম কোনো একটা জায়গায় খবরের কাগজ বিছিয়ে বসে থাকব। হাতে একটা প্ল্যাকার্ড রাখব সেখানে লিখব, ""প্রশ্ন ফাঁস মানি না, মানব না। আমাদের ছেলে-মেয়েদের অসত্ হতে দেব না।""....sir i m with u",0,celebrity
"সার, আজকে ১৭ আগস্ট! :/",0,celebrity
"ভালবাসি স্যার। বেচে থাকুন অনন্তকাল, আপনাকে এই ঘুণে ধরা সমাজের বড়ই প্রয়োজন।",0,celebrity
"আজকাল আর ট্রল পেজ গুলায় যাওয়া লাগে না ট্রলের জন্য। আপনাদের মত বুদ্ধিজিবিরাই যথেষ্ট বিনোদন দেন৷ :) কেন যে এই রকম নির্লজ্জ দালালি করেন, বুঝে আসে না। অবশ্য সোনার বাংলাদেশ, যে যেইভাবে পারে সেইভাবেই ফায়দা লুটে যায় দেশটার।",0,celebrity
Psc/jsc/ssc/hsc Exam Suggetion and Question Help Line. P.S.C পরিক্ষা বাংলাদেশ ও বিশ্বপরিচয় প্রশ্ন লাগবে কার ? এবং বোর্ডের নাম উল্লেখ করো । Typing চলছে...... বাংলাদেশ ও বিশ্বপরিচয় রচনামূলক প্রশ্ন : ক . মনে করো গত সপ্তাহে তুমি বাংলাদেশের ১টি ঐতিহাসিক স্থানে পরিদর্শন করেছো - এ সম্পর্কে ৫টি বাক্য লিখ । খ . বুদ্ধিজীবি কারা ?_________________ ___________ এখন একটা প্রশ্ন দিলাম । পরবর্তী আপডেইট পেতে লাইক এবং কমেন্ট করুন ।        এইগুলা কি স্যার? আমাদের বাচ্চা দের কি শেখাচ্ছে? বাংলাদেশের ভবিষ্যৎ কি স্যার?  একটু বলেন প্লিজ।,0,celebrity
আরে মাইগ্গা,0,celebrity
এতো বড় স্ট্যাটাস দিয়েন না। পড়তে সময় লাগে। আমার হাতে এতো সময় নাই। যা কইতে চান ঝটপট সাদাসিধে লিখে ফেলবেন৷ আর লেখায় প্যাঁচ না রেখে সরল কথায় মূল বক্তব্য তুলে ধরার বিশেষ অনুরোধ রইল। ধন্যবাদ,0,celebrity
"এক ভাই কমেন্ট করছেন, সার কিছু জানে না, দুদু খায়৷ আমি জানতে চাচ্ছি- উনি কীসের দুদু খান??",0,celebrity
ছাত্ররাজনীতি বাংলাদেশ থেকে নিষিদ্ধ করা হোক।যতদিন ছাত্ররাজনীতি থাকবে ততদিন বাংলাদেশ উন্নত রাষ্ট্রে পরিণত হবেনা। ছাত্ররাজনীতি দেশ ও জাতিরর জন্য অভিশাপ।জাফর ইকবাল স্যার আপনি একজন শিক্ষক ও বিখ্যাত মানুষ।দয়াকরে ছাত্ররাজনীতির বিরুদ্ধে কলম ধরুন।,0,celebrity
"স্যার, খোদার উপর আস্থা রাখুন...!! আর কয়দিন নাহ... অনেকদিন আপনি বেঁচে থাকবেন....!! 😋",0,celebrity
মাহমুদ ভাইয়ের কথাটা শুইনা যান 😂😂 Manowar Mmc Sayedur Rahman Md Taher Md Rifat Chowdhury দাদার লাঠি HT Sadia মু. লাবিব আহসান Hashan Mahmud Ruhul Amin Tamim,0,celebrity
আসলে কি ফ্যারাডে o aki somossay pore clo.Ter amole o sobai procolito sob kicu niye vabta ja amader mukhosto bidday sikhito r ortha lovi kicu sir kortece.Einestine o nijek murkho vebe clo keno na se procolito niom er baire vabto bole.Kin ai vabnai ta k aj ato ta boro korece.Amr kosto lage tokhon j Amader desh er Boro boro amla r professor ra sudhu shopno dekhan but Boro hole aki kotha bolen hoy doctor/eng. hote hobe tao aber guti koek subject er eng/doc hote hobe.Keno ei rokom vaben tara.1 ta designer o to 1 jon valo eng./1 jon valo sergeant o to valo doc.Asha kori amra ai vul gulu shudrate parbo.,0,celebrity
বিনো ধোন  নিতে আসলাম। কমেন্ট পড়তেছি,0,celebrity
আমার মন মানসিকতা যদিও ভাল ছিল না তবুও আপনার পোষ্ট থুক্কু পোষ্টের কমেন্ট গুলা পরে মনটা ভাল হইয়া গেল।,0,celebrity
স্যার এই পোস্টটি পড়ে কেঁদে ফেললাম অামি। কারণ অনেক ভালবাসি অাপনাকে। <3  তাড়াতাড়ি সুস্থ হয়ে উঠোন অাপনি এটাই অাশা করি  অনেক ভালবাসি অাপনাকে।,0,celebrity
"স্যার, আপনার জন্যে আন্তরিক ভালোবাসা আর বিনম্র শ্রদ্ধা <3",0,celebrity
"স্যাড় একটু ভুল হয়েছে! নারীরা বাইক চলিয়ে সাহসী নারী হতে পেরেছে, কিন্তু পুরুষরা সাহসী পুরুষ হতে পারেনি এক্ষেত্রে পুরুষরা একটু পিছিয়েও আছে😇",0,celebrity
হাগু দিলাম,0,celebrity
আমি নিবন্ধন পরীক্ষার সাজেসন্স চাই,0,celebrity
স্যার বহু বহু দিন বেঁচে থাকুন আলোর মশাল হয়ে,0,celebrity
"আপনি নাকি লাইভ বুঝেন না, অনলাইনে ঢুকেন না, কিছু বুঝেন না। তবে বিবিসি,আল জাজিরার খবর কিভাবে রাখেন?",0,celebrity
"পা চাঁটা গোলাম,মুক্তিযুদ্ধের সময় বিড়ালের মত গর্তে লুকিয়ে ছিলি এখন বড় বড় কথা বলিস।",0,celebrity
"চাকরীর পরিক্ষার ক্ষেত্রেও এরকম ব্যবস্থা করা উচিত।   একই গ্রেডের বিভিন্ন মন্ত্রনালয়, অধিদপ্তর, পরিদপ্তরে বিভিন্ন সময় আলাদা আলাদা সার্কুলার হয়। এতে করে প্রত্যেকবার আলাদা করে আবেদন ও পরীক্ষা দেয়া ব্যয়বহুল। যা একজন বেকারের জন্য খুবই কষ্টকর।",0,celebrity
"স্যার,অ স্যার,ফেসবুকে sarcasm একটা পেজ আসে   কিছু শিখেন",0,celebrity
এই লেখার প্রতিটি বাক্য আমার হৃদয়ের কথা। দীর্ঘ প্রবাস জীবনে অনেক অনেক বাঙালি দেখেছি যারা এক ধরনের হীনমন্যতায় ভোগে। আর সেই থেকেই যা না তাই বলে।,0,celebrity
"স্যার, পল্টিবাজ কথা বন্ধ করেন।  এতকিছুর পরেও আপনি বলতেছেন জানি না। অথচ ঢালাও ভাবে পক্ষ টেনে কথা বলছেন৷ আর কতভাবে কতজন এর কাছ থেকে সুবিধা নিবেন??  অনেক তো হইলো।  আপনি অনেক বড় মাপের মানুষ।  আপনি যখন জানি না বলে পক্ষপাতিত্ব করবেন তখন অসম্ভব রকমের খারাপ লাগে। তাছাড়া শহিদুল আলম কি তা আমাদের চাইতে আপনিই মে বি বেশি জানেন।  সুতরাং সুশীলতা বর্জন করুন।  জনগণ কে বিনোদন এর থ্রেশলড লেভেলে পৌঁছায় দিলে এই লেখার মাধ্যমে। মজা আমরাও পাইছি, মজা মনে হয় আপনিও পাইছেন। 😆😆",0,celebrity
জানাযা পড়ার পরে এই কথা কেন বললেন স্যার🐸,0,celebrity
খারাপ কমেন্ট করা মানুষ গুলো একেকটা শুয়োর ও পাকি বীর্যের মাল্টি কম্বিনেশনের ফল। যার নিক নেইম- ছাগু,0,celebrity
মাথা ব্যথা করতেছে ভাবছি ঘুমাবো।তখন দেখি জাফর কাকার পোষ্ট সামনে এসেছে।আর কি ঘুমানো যায়।বিনা পয়সায় বিনোদন নেওয়া জন্য কাকার কমেন্ট বক্স কিছু পড়ে নিলাম।,0,celebrity
"কবরের উপর দিয়ে যাওয়া সাপটারে লাঠি দিয়া ওভাবে মেরো না, আল্লাহ তোমাদের শাস্তি দিবো। তবে হ্যাঁ! পথে পথে কবি লেখকদের দা ছুরি দিয়া কুপিয়ে কুপিয়ে মারো, আল্লাহ তোমাদের শান্তি দিবো। 😭 😭 😭 😭 স্যার। সুস্থ হয়ে উঠুন। ঈশ্বর আপনার মঙ্গল করুক।",0,celebrity
"আপনাকে আমেরিকা চিনে নাই, চিনলে সেখানেই রেখে দিতো। একবার নয়, কয়েকবার নোবেল পুরষ্কার পাইয়ে দিতো। আপনি হতেন নোবেলে চ্যাম্পিয়ন যা এখনো কেউ হননি। কেন যে বাংলাদেশে পড়ে আছেন এই গর্দভের গর্তে। আর শুনুন, আপনার যুদ্ধে যোগ না দিয়ে ট্রেঞ্চ বানানোর গল্প সবাই জানে। আসলে ফাঁকিবাজিটা ওইখানেই শুরু। এমন বাটপারের দেশে ক্লাসে পড়ান বাদ দিয়ে কোচিং এর দিকে ঝুঁকবে, এ আর এমন দোষ কি?",0,celebrity
মান সম্মত এবং যুগোপযুগী পোষ্ট।,0,celebrity
রাজাকারের বাচ্চারা কি বাজে কমেন্ট করছে।,0,celebrity
হ্লারে কেউ মদ খাবা,0,celebrity
আইলাম কমেন্ট পরার জন্য ষারের লেখা পড়ার জন্য আসি নাই। 🐸😂,0,celebrity
"ধন্যবাদ স্যার সত্যে তুলে ধরার জন্য,, রাজাকার এরবাচ্চারা খারাপ কথা বলবেই,, কারণ ওদের শরীর এ তো রাজাকার এর রক্ত।",0,celebrity
কিরে ভাই তুমি বাঁচি আছনি,0,celebrity
"শ্রদ্ধেয় জাফর ইকবাল স্যার,আপনার গায়ে একজন আঘাত করায় আপনার লাখ লাখ সন্তান সারা দেশে আন্দোলন করলো । শুনেছি শিক্ষক মা বাবার পরেই যার স্থান । আজ আপনারই সন্তানের গায়ে হাত তোলে,মেরে রক্তাক্ত করে আরো মারে,আপনারই কোনো মেয়ের পায়ের রগ কেটে দেয় । তারপরও আপনি কেমনে নিরব আছেন",0,celebrity
"ইসলাম নিয়ে বাজে মন্তব্য কোন মুসলমানের সহ্য হবেনা, তাই বলে তাকে রাস্তায় কুপিয়ে মেরে ফেলা হোক এটাও ইসলাম সমর্থন করেনা, যেটা মানুষ সৃষ্টি করেনি সেটা ধ্বংস করার অধিকারও তার নেই, যদি সে আল্লাহ্‌ কিংবা রাসুলকে নিয়ে বাজে কিছু বলে থাকে তাহলে সেই বিচার আল্লাহ্‌ করবে, আল্লাহ্‌ যদি কোন নাস্তিককে নিজের দয়া দিয়ে বাঁচিয়ে রেখে খাওয়ায় পড়ায় তাহলে আপনি কে তার প্রাণ নেওয়ার? হাশরের ময়দানে কী জবাব দেবেন? যারা এই ধরণের কাজ করে তারা আসলে মুসলমানই না আমি মনে করি, জন্মসূত্রে ইসলাম পরিবারে জন্ম গ্রহণ করলেও এরা আসলে মুসলমান নয়, এরা হল নিচু শ্রেণীর কিছু প্রাণী, এদের কোন নাম নেই, নামের জন্য যোগ্য হতে হয় কিন্ত এরা হল নিচু শ্রেণীর প্রাণী, মানুষ কুপিয়ে কোন ইসলাম প্রতিষ্ঠা করছে কীভাবে করছে জানিনা। নবীজির যুগেও ইসলাম নিয়ে কটাক্ষ করা হয়েছে, নবীজিকে পাথর মারা হয়েছে তাই বলে নবীজি রাতের বেলা ওদের ঘরে গিয়ে কুপিয়ে আসেনি বরং নম্রতা এবং সহনশীলতা দিয়েই তাদের মন জিতেছে, আমি বলব যারা এই ধরণের কাজ করে তারা বরং ইসলামের শত্রু, তাদের কারণে ইসলামের উপকার তো দূরের কথা বরং ক্ষতি হচ্ছে, অভিজিতের খুনের কারণেই কারণেই অনেকের এখন ইসলামের প্রতি ক্ষোভ তৈরি হয়েছে, এখন কী করবেন? ওদেরকেও মেরে ফেলবেন? আল্লাহ্‌ আপনার প্রতিটা কাজের হিসাব নেবেন বিশেষ করে যুবক বয়সের, তখন কী বলবেন? মানুষ মেরে আপনি ইসলাম রক্ষা করেছেন? আল্লাহ্‌কে রক্ষা করেছেন?  তবে দেশে ধর্মনিন্দা অনেক বাড়ছে, এজন্য ব্লাসফেমি আইন প্রতিষ্ঠা করা প্রয়োজন আমি মনে করি, তাহলে সরাসরি কেউ ইসলাম কিংবা অন্য ধর্মের নিন্দা করার সাহস পাবেনা, যদি কেউ করে তাহলে আদালতে হাজির করে বিচার করা হবে, রাস্তা কুপিয়ে নয়",0,celebrity
কেউ আমার হাসতে হাসতে মুতে দিয়েন না সাবধান ভাইয়েরা।। আমি কিন্তু দিয়ে দিছি 😞😞,0,celebrity
"বুদ্ধিজীবীরা তিনভাগে বিভক্ত, ভণ্ড, ভণ্ডতর, ভণ্ডতম, হূমায়ন আজাদ।",0,celebrity
উনি বেঁচে উঠলেন কিভাবে??,0,celebrity
"""ঊর্ধ্বশ্বাসে ছুটিতেছে চাটুকার  কে কাহার আগে চাটিবে পা 'তাহার'!""  #সংগৃহীত",0,celebrity
যেখানে আপনার গায়ে আঘাতের জন্য ছাত্র-ছাত্রীরা আন্দোলন করেছিল আজ সেই জায়গায় আপনি আপনার কর্তব্যটা ঠিকভাবে পালন করেছেন স্যার। আপনার ছাত্র হয়ে শিক্ষা পাওয়াটা সত্যিই ভাগ্যের ব্যাপার।,0,celebrity
"আমি আমার পরিচিত জগতের সব মানুষকে দু’ভাগে ভাগ করে ফেলেছি। এক ভাগ হচ্ছে যারা উৎসাহী, অন্য ভাগ হচ্ছে যাদের কিছুতেই উৎসাহ নেই, যাদেরকে ঠেলাঠেলি করে নিয়ে যেতে হয়! উৎসাহীরা পৃথিবীটাকে চালায়, বাকিরা তার সমালোচনা করে! great writing....",0,celebrity
"ক্রেনিয়াল সায়েন্সফিকশন আমার ফেভারিট একটা বই,,",0,celebrity
আপনি এক জনের না হয়ে সবার জন্য হলে বোধকরি আরো ভালো হতো। হয়তো দালাল নামক শব্দটা নামের পাশে দেখতে হতোনা।,0,celebrity
"কোথাও তিনি তার লিখায় এই আন্দোলনের সাথে একাত্মতা প্রকাশ করেন নি।  স্যার,আমরা অল্প হলেও বুঝি। আপনার থেকে এসব আশা করা যায় না।",0,celebrity
উনি কি টেকনোক্রেট মন্ত্রী হবেন? 😇,0,celebrity
"সুন্দর গল্প, কফি করা নাকি 😎",0,celebrity
কমেন্ট পড়ার জন্য আমি কমেন্ট বাক্সে অপেক্ষমান।,0,celebrity
তৈলাক্ত কোন বইটই নাই মামু ?,0,celebrity
"স্যারের তো ঘুম ভাঙছে, গায়েবানা জানাজার কি হবে এবার? 😂😂",0,celebrity
"স্যারের পায়ের নখেরও অযোগ্য অমানুষের বাচ্চারা যখন বাজে কমেন্ট করে, তাদের জন্ম পরিচয় নিয়ে সত্যিই সন্দেহ হয় :) পাকি কুলাংগারগুলা কে দেশ থেকে তাড়ানো গেলেই দেশে শান্তি আসবে",0,celebrity
"পাগলা #ষাড় ক্ষেপেছে স্ট্যাটাস দিয়েছে আহাহাহাহাঃ উঃ বড্ড লেগেছে।  পুনর্জন্ম গ্ৰহন করাই #সেলযোগ বংশের  শাহজাদা ইগিত এর পক্ষ থেকে মোবারকবাদ 😊  ষাড়, বিষ দে  মদ খাবো  না মদ দে বিষ খাবো হবে?",0,celebrity
প্রচুর হাহাহা হবে,0,celebrity
"বঙ্গবন্ধুর অতি কাছের মানুষ তার রাজনৈতিক সচিব তোফায়েল আহমেদ বসে আছেন রক্ষীবাহিনীর সদর দপ্তর সাভারে । আতঙ্কে তিনি অস্থির । বঙ্গবন্ধু নিহত হলেন । বঙ্গবন্ধুকে রক্ষার দায়িত্বে নিয়োজিত রক্ষীবাহিনী ঝিম ধরে বসে আছে । একসময়ের সাহসী তেজি ছাত্রনেতা তোফায়েল আহমেদও ঝিম ধরে বসে আছেন । শুরু হয়েছে ঝিম ধরার সময় । রাস্তায় মিছিল বের হয়েছে । দুর্ভাগ্যজনক হলেও সত্যি , সেই মিছিল আনন্দ মিছিল । শফিক বাংলামোটরে গিয়ে এক অদ্ভুত দৃশ্য দেখল । সেখানে রাখা ট্যাংকের কামানে ফুলের মালা পরানো । কিছু অতি উত্সাহী ট্যাংকের উপর ওঠে নাচের ভঙ্গি করছে । আমার বাবর রোডের বাসার কথা বলি । বেতারে বঙ্গবন্ধুর মৃত্যুর খবর প্রচারের সঙ্গে সঙ্গে একতলার রক্ষীবাহিনীর সুবেদার পালিয়ে গেলেন । তার দুই মেয়ে ছুটে এল মা’র কাছে । তাদের আশ্রয় দিতে হবে । মা বললেন তোমাদের আশ্রয় দিতে হবে কেন ? তোমরা কি করেছ ? তারা কাঁদো কাঁদো গলায় বলল , খালাম্মা , এখন পাবলিক আমাদের মেরে ফেলবে । এই ছোট্ট ঘটনা থেকে রক্ষীবাহিনীর অত্যাচার এবং তাদের প্রতি সাধারন মানুষের ক্ষোভ ও ঘৃনাও টের পাওয়া যায় । (দেয়াল, পৃষ্ঠা-১০৭)।",0,celebrity
আপনার নামে বিটিভির নাম করন করার দাবী জানাচ্ছি। জোর দাবী।,0,celebrity
আবু সাদাত মোহাম্মদ সায়েম,0,celebrity
"সিলেটে গাজার বাম্পার ফলন,,, মাতালরা খুশি তে খাসি হয়ে যাচ্ছেন..... BTV",0,celebrity
"যারা গায়েবানা জানাযা পড়েছেন তারা হয়ত জানেন না ড. মুহাম্মদ জাফর ইকবাল আপনার বা আমার মত অ্যাকটিভ ফেসবুকার নন, তাঁর ফেসবুক আইডি নেই। এই পেইজটি তাঁর ছাত্ররা চালায়। খেয়াল করে দেখুন এখানে দিনে ২টি পোস্ট উগড়ে দেওয়া হয়না। ৮/১০ দিন বাদে একটি লেখা আসে। প্রতিটি ইস্যুতেই তাঁর কিছু লিখতে হবে এমন কোনো বাধ্যবাধকতা নেই। তবে দেশের সেরা ব্যক্তিত্বদের একজন হওয়ায় আমরা তাঁর দিকনির্দেশনা আশা করি। কিন্তু কেন তিনি কিছু বলছেন না এটা ভেবে তাচ্ছিল্য করতে পারিনা। এমনই যদি হতো তবে দেশে কি আর কেউ নেই? প্রভাবশালী ব্যক্তিবর্গ? তাঁদের কাছেও কিছু আশা করুন। কিছু হলেই জাফর ইকবালকে টেনে হিঁচড়ে নামানোর আগে ১০বার ভাবুন আপনি তাঁর সমালোচনা করার যোগ্য কিনা।",0,celebrity
"এই যদি হয় বাংলাদেশের সেরা একজন লেখকের দায়সারা লেখার মান....রাশেদ ভোই, মেজর ডালিম ভাই, নোমানি ভাই পিনাকি স্যার, বৈরম ভাইদের প্রতিবছর নবেল পাওয়া উচিত।",0,celebrity
"ছোটবেলা থেকে আপনার গল্পের বই পড়ে বড় হয়েছি, নায়কের আসন থেকে আপনার ছুড়ে ফেলতে নিজের কাছেই খারাপ লাগছে। আপনি জনগনের পালস বুঝেন না? কিজন্য এমন দলকানা হয়ে গেলেন? ছিহ",0,celebrity
স্যারের দ্রুত আরোগ্য এবং দীর্ঘায়ূ কামনা করি।,0,celebrity
"এক কোটা নিয়া মাদারটোস্ট দের চেতনা  খাড়াই উদলাইয়া পড়তেসে,আর যে মাদারচোদরা তোগোর মা-বোনরে পাকিদের ধনের উপর বসাই দিসিলো হেইদা তোরা এত সহজে ভুইলা যাস...জামাতী ভাষায় কথা কস...পাকিরা আসলেই ভালই স্পার্ম ভইরা দিয়া গেসে, পাকিরা এই ভএাইবা খুসি যুদ্ধে হারসি তো কেয়া হুয়া আঠা তো সেহি যাগা পে রাখ দিয়া",0,celebrity
"কোরআনে অবিশ্বাস্য বর্ণ ( letter) মিল!!!!!  কোরআনে আল্লাহ বলেন যে নূহ আঃ এর  বয়স 950 বছর উল্লেখ করেছেন  ৷ এটা একটা সাধারন ব্যাপার, তাই না???? চমকে যাবেন আসল তথ্য শুনলে!  সূরা আল আনকাবূত এ আল্লাহ বলেন   [14] وَلَقَد أَرسَلنا نوحًا إِلىٰ قَومِهِ فَلَبِثَ فيهِم أَلفَ سَنَةٍ إِلّا خَمسينَ عامًا فَأَخَذَهُمُ الطّوفانُ وَهُم ظٰلِمونَ [14] আমি নূহ (আঃ) কে তাঁর সম্প্রদায়ের কাছে প্রেরণ করেছিলাম। তিনি তাদের মধ্যে পঞ্চাশ কম এক হাজার বছর অবস্থান করেছিলেন। অতঃপর তাদেরকে মহাপ্লাবণ গ্রাস করেছিল। তারা ছিল পাপী।  বিস্ময়কর ব্যাপার হল কোরআনে "" সূরা নূহ ""নামে একটি সূরা রয়েছে ৷ আপনি জানেন এই সূরায় কতটি বর্ণ ( letter) ????  সূরা নূহে বর্ণ  সংখ্যা ঠিক 950 টি!!!!  কেন 950 টি?? 949 হল না কেন??? 951 টি হল না কেন???? কেন এভাবে বিস্ময়কর ভাবে কোরআনে বর্নিত  নূহ আঃ এর বয়সের সাথে মিলে গেল??? কেন কম বা বেশি হল না????   এটাও কি একটি কাকতালীয় ব্যাপার???? অবশ্যই না, মূলত কোরআন, আল্লাহ তায়ালার বাণী বলেই এভাবে একের পর এক সংখ্যা মিলে যাচ্ছে ৷",0,celebrity
ধন্যবাদ স্যার ! কথাটি স্মরনকরিয়ে দেবার জন্য !,0,celebrity
Zafar is not worthy to be respected.  He is just a cheap work for awamileague...,0,celebrity
"ঘুমায় পড়েন প্লিজ! আপনি কমেন্ট বক্স দেখিয়েন না আজকে! বুক ব্যাথা আছে? মেডিসিন নিয়েন কিন্তু! নয়ত ব্রেকিং নিউজ হবে 'ইতিহাসে প্রথম ফেসবুকে স্ট্যাটাস  এর কমেন্ট পড়ে ডক্টর এর মৃত্যু!' বাই দ্যা ওয়ে,কমেন্ট ডিলিট করার জন্য লোক ভাড়া করছেন তো? :-/",0,celebrity
কমেন্ট দেখে বোঝা গেল স্যার জাফরের ভন্ডামি আর লোকে খায় না। অনেক তো চেস্টা করলি কিন্তু ভারতিয় চেতনা এখন আর মানুষ নেয় না।,0,celebrity
হর হর করে মধ্যাঙ্গুলি দেখাইলাম😂😂😂,0,celebrity
কেউ ঠ্যালাঠেলি করবেন না প্লিজ লাইনে দাঁড়ান সবাইকে গালি দেওয়ার সুযোগ দেওয়া হবে :3,0,celebrity
টাট্টি ইকবাল ব্রো 😄 তর পোস্টে কমেন্টে পড়ে হাসতে হাসতে পাশের বাড়ির ভাবিকে ভুল করে পাপ্পি দিয়ে বসলাম 😊😊😊😇😇😇😇😇😇,0,celebrity
স্যার দোয়া করছি আপনি শীঘ্রই আমাদের মাঝে ফিরে আসবেনই.- লক্ষ কোটি আপনার ভক্তরা আপনার অপেক্ষায়,0,celebrity
কবির গভীর ধ্যানমগ্ন থেকে এসেছেন বুঝতে হবে ওনি লেখক ধ্যান মগ্ন করেই লিখতে হবে। সময় লাগে... “কবর থেকে বলছি “ এই শিরোনামটাই বেশ মানাতো 🤣,0,celebrity
এই প্রযুক্তির আমলে আপনি ইউটিউব ফেইসবুক ইন্টারনেট ছাড়া কাটান আবার নিজেরে বিজ্ঞান মনস্ক দাবি করেন কেমনে? এমন তো না যে আপনার শ'খানেক পিয়ার রিভিউড জার্নাল আছে আর আপনি সারাদিন গবেষণায় ব্যস্ত থাকেন? ভোগাস।  চোস্ত মিথ্যুক আপনে।,0,celebrity
স্যার...আপনার মত মেধাবী মানুষ আমেরিকা তে বড় প্রয়োজন... আমেরিকাতে নিরাপদ সড়ক চাই নিয়ে আন্দোলন হয় না...,0,celebrity
এসব ঘটনা প্রকৃত মুজিব প্রেমিদের কতটা কষ্ট দেয় সেটা সেই জানোয়ার গুলা বুঝে না। অবস্য তারা না বুঝাই স্বাভাবিক,0,celebrity
আমরা চট্রগ্রামে ও শুরু করতে চাই এ আন্দোলন.........,0,celebrity
yes.jara baje montobo kore tader ban korun,0,celebrity
হাইস্যকর,0,celebrity
এখনই হড়হড় করে বমির শব্দ....... ইসস বললাম না! এখনই হড়হড় করে বমি করে দেবে,0,celebrity
"লা হাওলা ওয়ালা! করসিডাকি আমি। আমিতো মনে কচ্চিলাম আফনে গেচেন, গায়েবী জানাজায় যাওয়ার প্রস্তুতিও লইয়া লাইসিলাম!!",0,celebrity
আহা।  আমরা  কি ভুল করে পেলেছি উগান্ডা। উনি বেচে থাকতেই ফেসবুকে উনার জানাজা দেখে পেলেছি। আহা,0,celebrity
তোমার মত ছাগলে নির্বাচন নিয়ে না ভাবলেও চলবে,0,celebrity
জাফর ইকবাল স্যারের বয়স হয়েছে জানিনা কতদিন বাচবেন তবে আমরা চাই তিনি দীর্ঘজীবন পান! একটি কথা তিনি শিক্ষা নিয়ে কাজ করছেন! স্যার যদি প্রশ্ন ফাঁস বন্দ্ধ করতে পারেন তাহলে স্যার অবিস্মরণীয় হয়ে থাকবেন,0,celebrity
আপনার মত লোক এখনো বেঁচে আছে বলে দেশ বিনোদনের অভাবে পড়েনি এভাবেই বিনোদন দিয়ে পাশে থাকবেন! 🐸,0,celebrity
"কোকেনে আলকোহল খুব বেশি চিল কি,ঘুম ভাঙার পরও,ঘুমের ঘোরে পোস্ট দেওয়ার মানি কি।",0,celebrity
"এভাবে বলে না, ছী : । উনার ""হড়হড় "" করে বমি হচ্ছিল ! যার জন্য দায়সারতে দেরি হল। একজন অসুস্থ ব্যক্তির প্রতি সমবেদনা জ্ঞাপন করেন। পশ্চাৎদেশটা এমনিতেই ব্যথাই কাতর, আর দিয়েন না",0,celebrity
"স্যার, আসুন। নামায পড়ি।",0,celebrity
"ও আমার মাসিক বিনোদন তাহলে এসেই গেছে! বিনোদন নিতে আইলাম!  শাসকশ্রেণী এই তোতাপাখিটাকে দিয়ে আমাদের কিছু সত্যমিথ্যা গুলিয়ে খাওয়াতে চায় বারবার।  আমি বুঝিনা এই মানুষটি এত শিক্ষিত হওয়ার পরও,  তার এই তোতাবৃত্তিতে কি স্বাদ পায়?  প্রভুর গোলামের গোলাম!",0,celebrity
"আমি পরীক্ষার প্রশ্নপত্র দেখিনি, ইংরেজি বিভাগে ভর্তি হওয়ার জন্য কী কী যোগ্যতা চাওয়া হয়েছে, তার খুঁটিনাটিও জানি না।- kono kichu na dekhe montobbo korata apner moto geyani loker kache kammo noy.....soisob koisor purotai keteche apner lekha boi pore, apnake ekjon adorsho manush mone kore, kintu bigoto bochorguloy apner sorkarer tel marar beparta selucas.....apner r apner montrir prosonopotro peye bostavora golden diye kicchu ase jay na...taderke apnarai medhabi bolben r keo na নতুন নিয়ম অনুযায়ী ইলেক্টিভ ইংলিশ এ উত্তর করলেই শুধু মাত্র ইংরেজি বিভাগে ভর্তি হবার নিয়ম এবছর চালু হয়েছে। এবং ইলেক্টিভ ইংলিশ এর উত্তর করেছে ২৬ জন।পাশ করেছে ২ জন।এটা সবার অংশগ্রহনের ফলাফল নয়।",0,celebrity
"আপনার ""আমার বন্ধু রাশেদ"" বইয়ের উপর করা সিনেমা দেখে আপনার প্রেমে পরেছিলাম তারপর আপনার প্রতিটি লেখাই আমার প্রিয় থেকে প্রিয় হতে থাকে।মানুষ হিসেবে আপনি যাই হন না কেন আপনি আপনার জ্ঞানের দ্বারা একটা জাতির তারুণ্যকে পরিবর্তন করার ক্ষমতা রাখেন। আল্লাহর কাছে দোয়া করি আপনি তাড়াতাড়ি সুস্থ হয়ে আমাদের মাঝে ফিরে আসেন।",0,celebrity
"স্যার, আর কতকাল দালালী করবেন...?  আমরা সাধারণ ছাত্ররা তো আর আপনার মতো দালালদের মুখে বমি করতে পারি না...  তবে আপনার মতো পা-চাটা প্রাণিদের পেজ আনলাইক দিতে পারি...",0,celebrity
বাস্তবে খুব বেশী ঘনিষ্ঠতা দেখা না গেলেও মৃত্যুর পর হুমায়ুন স্যারের লাশ নিয়া চেস্টা করছিলেন। শাওনের কাছে হেরে গিয়ে রণে ভংগ দিয়েছেন। দয়া করে আপন বড় ভাইয়ের কাছ থেকেও হলে ন্যুনতম শিক্ষাটা নেন। এক্বেবারে দাসত্বের জীবন আর কত দিন চালাবেন! অন্ধ চামচামির ফোয়ারা আর কতো দিন ছুটাবেন!!,0,celebrity
"স্যার,ছোট বেলা থেকেই আপনার লেখা পড়ি,আপনার লেখায় এক ধরনের টান অনুভব করি।সর্বশক্তিমানের কাছে প্রার্থনা করছি, তিনি যেন আপনাকে দ্রুত সুস্থ করে দেন, প্রতিটি মূহুর্ত ইমানের সাথে রাখেন এবং নেক হায়াত দান করেন। আমীন।",0,celebrity
সবাই নাকি কমেন্ট পড়তেছে..?😊,0,celebrity
"আপনার চুপ থাকা উচিত, একদম চুপ থাকা উচিত...",0,celebrity
আপনার মতো ষাঁড়দের এখন ভারতে খুব প্রয়জন কারন সেখানে এখন সমকামিতা বৈধ  আপনার মতো অপদার্থ কোন নাস্তিকের জন্য হয়তো কোন সমকামি অপেক্ষা করছে আর দেরি না করে আপনাদের ভারত মাতার কাছে ফিরে যান আর অবলিলায় গো মূত্র পান করুন,0,celebrity
জাফর সাহেবের বমি অাসে এটা উনার একান্ত সমস্যা।  যেটা শুনে ঘেন্নায় সারা দেশের মানুষের বমি হচ্ছে।,0,celebrity
"স্যার তো বিশিষ্ট খাট যোদ্ধা , বাংলাদেশে সমকামীর অভাবে তিনি আজ ভারতে। জয়তু",0,celebrity
মোঃ মেহেদী হাসান নাঈম,0,celebrity
আমগো স্যাররে কেউ একটা নমিনেশন দে...  স্যারের তেল ফুরিয়া যাওয়ার আগে কেউ নৌকাটা দে... আর সহে না...,0,celebrity
তেশ মারা ফাইনাল,0,celebrity
স্যার আপনিও অন্যান্য কবি-সাহিত্যিকগণের মতো হবেন না দয়া করে। লিখে যান অন্যায়ের বিরুদ্ধে।,0,celebrity
"প্রিয় স্যার, কি গভীর ভালবাসা নিয়ে মানুষ অপেক্ষা করছে, আপনার সুস্থ হয়ে ফিরে আসার জন্য, সেটা কি আপনি জানেন? একই পরিবারের সব গুলো মানুষ কি করে এত মানুষের ভালবাসা পায়? মহান আল্লাহ আপনাকে এবং আপনাদের যা দান করেছেন, তার তুলনায় অন্য সব কিছু তুচ্ছ। সবচেয়ে বড় কথা হচ্ছে, আপনি এবং আপনার পরিবারে সবাই ভালবাসা পাচ্ছেন তাদের, যারা নিজেরা কেউই একেবারে তুচ্ছ মানুষ নন। স্বশিক্ষিত, অনুভুতিপ্রবন, স্বাধিনচেতা, নিজের পায়ে দারানো ঝাকে ঝাকে মানুষ আপনাকে ভালবাসে। এদের ভালবাসা কিন্তু অত সস্তা নয়। অল্প কিছু চামচা, মানসিক অসুস্থ, মুসলমান নাম ধারি কিছু ধম্মহীন মানুষ আপনাকে ভাল না বাসলে কিই বা আসে যায়।  আল্লাহ নিশ্চয়ই আপনাকে আরও দিরঘায়ু করবেন। আমিন।",0,celebrity
"তর লিখা পড়িনা,তবে কমেন্ট পড়ি তারপর বুঝি আসলে তুই কতটা লিখতে জানস।",0,celebrity
"স্যার, আপনি এইসব ফালতু লোকদের কমেন্ট পড়ে নিরুতসাহিত হয়ে লেখা বন্ধ করে দিবেন না প্লিজ। বরং আমি আশা করব আজকের মত আপনি বৃহষ্পতিবারের পাশাপাশি প্রতি সোমবারেও একটি করে লেখা দিবেন আপনার পেইজে। আমি জানি, আপনার জন্য সময় জোগাড় করা কঠিন হয়ে পরবে কিন্তু প্লিজ আমাদের মত পাঠকদের দিকে চেয়ে আপনি সপ্তাহে অন্তত দুই দিন লিখবেন। এটা আপনার কাছে আমাদের দাবী। দেশে গোপাল ভার মরে যাবার পর তার স্থলে কেবল আপনাকেই পেয়েছি, আমাদেরকে বঞ্চিত করবেন না :-(  Ashraf shafi vai,,,, Valo laglo",0,celebrity
"""আমি দূর্বল প্রকৃতির মানুষ "" - তাহলে কলিকাতা হারবালে কেন যাচ্ছেন না?",0,celebrity
আর ছাত্র সমাজ আপনার উপর এখনই হড় হড় করে বমি করা শুরু করেছে তবে মুখে আঙুল দিয়ে নয় আপনার লেখা পড়ে অনইচ্ছাকৃত ভাবে তা বেরিয়েছে,0,celebrity
সেফুদা বলেছেন আপনার দাদা রাজাকার ছিলেন,0,celebrity
মদ খাচ্ছি আর কমেন্ট পড়ছি।,0,celebrity
এরকম একটা পোস্ট পাইলে আমি একটা কমেন্ট ও বাদ দিই না.. কি করতাম ভাল লাগে যে...,0,celebrity
"বিগ ব্যাঙ সম্বন্ধে পড়তে,জানতে খুবই ভাল লাগে!",0,celebrity
২নং আইডিয়াটা awsome!,0,celebrity
"স্যারের সার্কাজমটা বুঝতে আমার কয়েক মিনিট সময় লেগে গেলো! কমেন্ট পড়ে বুঝলাম, জাতি বেশ বেরসিক! ফানও বুঝে না... ইতিহাসের সর্বোচ্চ লাইকধারী নির্বাচন নিয়ে আপনারা কতোই না আনন্দ করলেন, স্যারও কি একটু মজা নিতে পারবেন না 😎",0,celebrity
"সার আমার ভোট টা কোন রাজাকার দিয়ে দেছে আমি দিতে পারিনি, সার তা হলে কি আমি বাংলাদেশি নাগরিক না, আপনার মতামত চাই 😩",0,celebrity
"ইন্নালিল্লাহি ওয়াইন্নাইলাইহি রাজিউন,",0,celebrity
রাস্তায় কেউ পাদ দিলে সবার আগে আপনি কিছু বলেন না কেন?  জাফর স্যার জবাব দ্যান?,0,celebrity
এসে গেসে চৌধুরী জাফরুল্লার ইশতেহার!,0,celebrity
কে তুই,0,celebrity
মুক্তিযুদ্ধকালে গুহাবাসীর মুক্তিযুদ্ধের চেতনা লালন করা আর আদার ব্যাপারীর জাহাজের খবর নেয়া একই কথা। ভাবছিলাম আজকেও হইত আপনি হড় হড় করে বমি করবেন। মাশাল্লাহ আপনি তো সুস্থ হয়ে গেছেন দেখছি।  আর শেষে লেখবেন বাচ্চারা তো রাস্তায় না নেমেও এমারজেন্সি লেন করতে পারত বা ট্রাফিক নিয়ন্ত্রণ করতে পারত।  তাই পুরো লেখাটা পড়লাম।  কিন্তু হতাস হলাম। ও হ্যা আপনার গায়েবানা জানাজা বাতিল করা হয়েছিল।,0,celebrity
"কে তুমি বৎস, ধরিয়া মৎস, বেচিয়া গঞ্জে, অকুল ও কুঞ্জে, না খাইয়া তাজা, কেনো ভক্ষন করিয়াছো মেয়াদ উত্তীর্ণ গাজা 😂😂",0,celebrity
হরহর করে বমি করে দিলাম স্যার।,0,celebrity
"স্যার ভোটগুলাও কি খা‌টের তলায় শ‌ু‌য়ে শু‌য়ে দি‌য়ে‌ছেন। আপ‌নি অ‌নেক বু্দ্ধিমান, যা শীতটাই না প‌ড়ে‌ছে। খাটই ভা‌লো।",0,celebrity
স্যার আপনি ত সুবিধাবাদী লোক। যখন দেখেন দেশে অরাজকতা চলছে মুখ খুললে সমস্যা হবে সরকার কতৃক তখন আপনি মুখ লুকিয়ে থাকেন গর্তে। যখনি অরাজকতা শেষ তখন আপনি গর্ত থেকে মুখ বের করে থুথু ফেলেন।,0,celebrity
আমরা কি আসলে দুরভাগা জাতি,0,celebrity
"মদ খা, মদ খা...",0,celebrity
কমেন্ট পড়তে আসলাম😂🙊,0,celebrity
সুন্দর বন কে আর বাঁচানো গেল না,0,celebrity
ধূর! সময় নষ্ট!,0,celebrity
"স্যার,  আপনাদের মত সুশিলদের জন্য আমাদের দেশের এ অবস্থা,  দেখেও না দেখার, বোঝেও না বোঝার ভান করে থাকেন।",0,celebrity
"উপরের ফটোতে দেইখাই বুঝা যাইতেসে যে হাতের প্ল্যাকার্ডের লেখাটা কম্পিউটারের ফন্টে লেখা! মানুষ ঐটারে আসল ভাবে ক্যামনে? আর যারা এই সব এডিটিং করে, ওদের জুতা মারা আয়োজন করা যায় কি!?",0,celebrity
স্যার ফিরে আসুন -  প্রানের সিলেট আপনার অপেক্ষায়......,0,celebrity
"আপনার মেয়ে অসুস্থ ছিল,  তাই অসুস্থতার দুর্ভোগ বুঝছেন।  যখন আপনার আত্বীয় যোগ্য চাকরি পাবে না, তখন আপনি কোটার ভয়াবহতা বুঝবেন। তখন রং পাল্টিয়ে সাধারনের কাতারে আসবেন।।",0,celebrity
"যারা প্রশ্ন করছেন স্যার কোনো কিছু না দেখে না শুনে না জেনে কেন এত বড় লেখা প্রসব করেন - তাদেরকে বলি, আপনারা কি ভুলে গেছেন স্যার গর্তে বসবাস করেন, ওখান থেকে এত কিছু দেখা শুনা জানা সম্ভব হয়না।",0,celebrity
"সমগ্র দেশে চলাচলরত যানবাহন এর লাইসেন্স চেক করা হোক ।লাইসেন্সবিহীন কোন বাহন রাস্তায় থাকবে না ।মালিকদের দক্ষ , দায়িত্বশীল ও সুস্থ  দেহ-মনের ড্রাইভার  নিয়োগ দিতে বাধ্য করে কঠোর আইন পাশ করা হোক । কিন্তু স্যার , অনেক দেরী হয়ে গেছে !   পুলিশ  তড়িঘড়ি করে শ্রাবনে নবান্ন (অসময়ে ট্রাফিক সপ্তাহ ) পালন করছে ।তবু দেখা যাক , ভালো কিছু হয় কিনা ।",0,celebrity
"থাক, কি দরকার এসব লেখার স্যার...!",0,celebrity
"স্যার আপনার প্রয়োজন আপাতত নেই, ৪ দিন পর আপনার ঘুম ভেঙ্গেছে,প্লিজ আবারো ঘুমিয়ে পড়ুন।",0,celebrity
"স্যার! নিজের দেশের নেত্রী যখন মুক্তিযোদ্ধারর সন্তান না হবার কারনে রাজাকার বলে গালি দেয় তার কষ্ট। আপনি কি বুঝবেন :)? যখন মুক্তিযোদ্ধা এর সন্তান না হবার জন্য ছাত্র জীবন,চাকরি জীবনে মেধা থাকা স্বত্বেও কোন সুযোগ পাওয়া যায় তার কষ্ট আপনি কি বুঝবেন? মুক্তিযোদ্ধা দের সম্মান সবাই করে! কিন্তু স্বাধীনতা যুদ্ধের সম্মান এক কথা আর তা নিয়ে পড়ে থাকা আরেক থাকা! ১৯৭১ এর যুদ্ধে দেশের অবস্থা না বরং ২০৭১ এ দেশের উন্নয়নকাজ করা এখন প্রধান! :) আর তা মুক্তিযোদ্ধার সন্তান না,একজন মেধাবী পারবে :)!!   আমার বাবা ও মুক্তিযুদ্ধে যোগ দেন নি তাতে কি উনি দেশ বিদ্রোহী হয়ে গেলেন?  সম্মান এক ব্যাপার আর সুযোগের অপব্যবহার আরেক!",0,celebrity
দালালি ছেড়ে সত্যের পথে আসুন। নামাজ পড়ুন আল্লাহ্ কে ডাকুন।,0,celebrity
পানিমন্ত্রীর লাইসেন্সহীন গাড়ি আটকিয়েছে শিক্ষার্থীরা; হেটে গন্তব্যে গেলেন মন্ত্রী,0,celebrity
তাড়াতাড়ি সুস্থ হন স্যার। আপনার জন্য ভালোবাসা♥♥,0,celebrity
"স্যার বমি করার পরের সিকোয়েন্স পার করে এখন সুস্থ হয়ে এই পোষ্ট টা দিয়েছেন,বাই দ্যা ওয়ে কেউ ঠেলাঠেলি করবেন্না সবাইকে সুযোগ দেয়া হবে ধন্যবাদ",0,celebrity
বমির রিয়েক্ট চালুর জন্য ফেসবুক কর্তৃপক্ষের নিকট জোর দাবি জানাচ্ছি :D।,0,celebrity
"স্যার, মুক্তিযুদ্ধের চেতনার নিরিখে এইবারের নির্বাচন নিয়ে অন্তত চারখানা লাইন যদি লিখতেন! আপনাকে আমিসহ অন্যান্যরা গালিমন্দ করি এটা আমার নিজেরই সহ্য হয় না। অতীতে আপনার লিখার প্রতিটি শব্দ কেমন উৎসুক হয়ে পড়তাম আর এখন তার উল্টাটা। আপনার বিরুদ্ধে দু একটা কথা চলে গেলে মানুষ ভাবে আমি আপনার হেটার্স ছিলাৃ অথচ আমার স্কুলের বন্ধুরা জানে কি পাগলই না ছিলাম আপনার লিখার জন্য। স্যার অনুরোধ রইলো, নিরপেক্ষ মন্তব্য করতে না পারলে আপনি লিখাই বাদ দিবেন। Good morning, good night, happy new year এইসব লিইখা ঘুমায়া পড়বেন। অন্তত আপনার বিপক্ষে কিছু বলবো না।",0,celebrity
স্যার! আমি তো হেফাজতী! আপনার সঙ্গে ১৫ এর বইমেলায় দেখা! সেদিন আপনাকে অনেক ভালো লেগেছে! বেশি ভালো লেগেছে আপনি আমাদের সমাজ সম্পর্কে জানতে চাওয়ায়! কিন্তু আপনার সামনে পিছু অনেক ব্যবধান!,0,celebrity
সাস্ট এ কত জন পরীক্ষা দিতে পারে,0,celebrity
"ষাড়,,,,আমরা দুঃখিত,,,ষাড় আপনি এত ঘাস খান তা আগে জানা ছিলনা😁😎😄🙏",0,celebrity
আদর্শ ভুলি আওরানো মানুষরা  নিলজ্জ মতো নৈতিকতা বিসর্জন দেয় যখন তখন তাদের মত কদাকার অন্য কিছু হতে পারেনা😞,0,celebrity
আমি সবসময়ই স্বপ্ন দেখি এই দেশের সরকারি দল আর বিরোধী দল দু’টিই হবে মুক্তিযুদ্ধের পক্ষের দল। দু’টি দলই বঙ্গবন্ধুকে বাংলাদেশের স্থপতি হিসেবে মেনে নেবে। যতদিন সেটি না হচ্ছে ততদিন গণতন্ত্র নিয়ে স্বপ্ন দেখার কোনো সুযোগ নেই।   অসাধারণ লাগলো স্যার,0,celebrity
"এসব নারীকে পুরুষের ভিড়ে ঠেলে দিয়ে তাদের সর্বস্ব লুট করার ফন্দি ছাড়া আর কিছইু না!  নারীদের প্রয়োজনে শিক্ষা-দিক্ষার দরকার হতে পারে।কিন্তু তার মানে এই না যে তাদের জন্য নিরাপদ পরিবেশ নিশ্চিত না করে হায়েনাদের পালের মধ্যে ছেড়ে দিতে হবে।মেয়েদের ইজ্জত-সম্ভ্রম,জীবন ঝুঁকির মধ্যে ফেলে তাদের শিক্ষাঙ্গনে,কর্মক্ষেত্রে পাঠাতেই হবে এমন কোন কথা আছে?তাদের সত্বীত্ত,তাদের জীবনের দাম কি এতই কম?যে বস্তুবাদী শিক্ষা আর কথিত উন্নয়নের নামে তা লুটপাট হতে হবে?যে পরিবেশে তা অনিরাপদ, সেখানো নিরাপদ পরিবেশ নিশ্চিত না করা পর্যন্ত পাঠাতে নিষেধ করা তো শতভাগ যুক্তিপূর্ণ।আল্লামা আহমাদ শফি সাহেবের কথা বাস্তবা এবং শরীয়তের দৃষ্টিকোন উভয় দিক থেকেই সঠিক।নারীদের সরলতার সুযোগ নিয়ে,উন্নয়নের ধোঁয়া তুলে তাদের বোকা বানিয়ে ঘর থেকে বের করে এনে ধর্ষণ করার মতলব যাদের তারাই কেবল হুজুরের কথার বিরোধীতা করতে পারে।",0,celebrity
"জনাব ইকবাল, আপনি আসলে কী খেয়ে বাঁচেন? রাখালের ওই পিঠা গাছের মতো আপনারও কোনো পিঠা গাছ আছে না কি? জন্মের পর কি চশমা ছাড়া পৃথিবী দেখার ভাগ্য আপনার হয় নি?",0,celebrity
"""তোমরা আমাকে ক্ষমা করো — আমি কিন্তু চেষ্টা করেছিলাম।""",0,celebrity
"দয়া করে আমাকে একটু জায়গা দিবেন? অনেকক্ষণ লাইনে দাঁড়িয়ে আছি। জাস্ট একটা কমেন্ট করব। প্লিজ, একটু জায়গা দেন🤣🤮",0,celebrity
দেখেন ভাই পাগল ছাগল নিয়া কমেন্ট করতে চাই না,0,celebrity
জাফর স্যার আপনাকে দেশের বেশীর ভাগ মানুষ ঘৃনা করে কেন সেটা কি অনুসন্ধান করে দেখেছেন? আপনার হওয়ার কথা ছিল প্রাতঃস্মরনীয় হলেন দেশের সবচেয়ে ঘৃনিত ও নিন্দিত মানুষ। আপনার নাম শুনলেই মানুষ গালি দেয়। আপনি মরে গেলেও মুক্তি পাবেন না। একজন ঘৃনিত অমানুষ হিসেবে এদেশের মানুষ আপনার উদ্দেশ্যে থুথু নিক্ষেপ করতেই থাকবে।,0,celebrity
স্যার... গম আছেন নি....আইতো মনে গইজ্জি তুয়াই গর্তত গেইয়োগ।।।।,0,celebrity
"আন্নের এইসব তৈলাক্ত মার্কা আবেগী কান্দন রাখেন মিয়া। পাবলিকের কাছে আপনার অবস্থান পরিষ্কার। এক কাম করেন, মুক্তিযুদ্ধ কালীন নয় মাসে  আপনার অবস্থান নিয়া একখান বই লেখেন।",0,celebrity
"স্যার, এর স্টাটাস টার সারমর্ম হবে কারো কাছে 😕",0,celebrity
"প্রকৃত ইতিহাস বলে, শেখ মুজিব রহমান কে জামায়াত বা জিয়াউর রহমান মারে নাই, সেনাবাহিনীর একদল মেজর বঙ্গবন্ধু কে গদি থেকে সরানোর জন্য গ্রেফতার করতে চেয়েছিল, কিন্তু মেজর নূর রাগের বশে সিড়িতে বঙ্গবন্ধু কে ব্রাশ ফায়ার করে, তার প্রমাণ বঙ্গবন্ধুর হাতের চূড়ুট, তিনি গ্রেফতার হবেন জেনে অন্য মেজর হুদা কে দিয়ে চূড়ুট এনেছিল। জাতীয় নেতা সৈয়দ তাজউদ্দিন আহমেদ ও চেয়েছিলেন অন্য  কোন নেতা গদিতে আসুক।  জেনারেল জিয়া আর খালেদ মোশাররফ জেনেছিলেন বঙ্গবন্ধু শুধু গ্রেফতার হবেন,  বাধা দিতে চান নি, তাহলে মেজর রা তাদের হত্যা  করত, সেনাবাহিনীর সবাই বঙ্গবুন্ধ আর ইন্ডিয়া কে এক চোখে দেখা শুরু করেছিল। বন্ধুবন্ধু নিদোষ ছিলেন,  তার কাছের চামচে দের জন্য মেজর দের রোষে পড়েন।  ইতিহাস এ তাই পড়েছি। এখন বলেন,  জামাত বা জিয়ার দোষ কোথায়? তাহলে তো জাতীয় বীর জেনারেল খালেদ মোশাররফ ও খুনি? সেনাবাহিনীতে মুক্তিযোদ্ধারা  সবাই তখন  কেন রাজনৈতিক কে পছন্দ করত না।  তারা বলত দেশ যখন স্বাধীন করলাম আমরা কষ্ট করে আর নেতা রা সব তখন কোলকাতায় মুরগী আর খিচুড়ি রান্না করে খেয়েছে। সেনাবাহিনীতে অনেক বই আছে সেগুলো ভাল করে পড়ে ইতিহাস জানুন।",0,celebrity
মন খারাপ?😂😂  এখন ভালো হয়ে যাবে😂😂 Redowan Rabby Fahim Montakim মন্দিরা সরকার,0,celebrity
স্যার অবশেষে বেঁচে অাছেন। উইকিপিড়িয়া তুই রাজাকার তুই রাজাকার,0,celebrity
রবিউল আউয়াল শরীফ ব্যাপী বেশি বেশি দরূদ শরীফ পাঠ করা ঈদে মীলাদুন্নবী সাল্লাল্লাহু আলাইহি ওয়াসাল্লামা পালনের অন্যতম সহজ ও শ্রেষ্ঠ মাধ্যম। ‎اللهم صل علي سيدنا محمد و علي ال سيدنا محمد بارك و سلم,0,celebrity
ভাই আমার তুমি কই কিছু কও...... জাতি তোমার সুবচন শুনিতে চায় Mainka Cipa,0,celebrity
অামার বন্ধু রাশেদ -২০১১  অামার শত্রু রাশেদ - ২০১৮  ---- জাফর ইকবাল,0,celebrity
"সবাই লাইনে দাড়ান, কেউ ঠেলাটেলি করবেন না,  সবাইকে সুযোগ দেওয়া হবে 😋",0,celebrity
এই গাঞ্জা খোর কয় কি?!! আম্রিকা বইসা ১৮ বছরের রিসার্চের ফলাফল এই? তয় কমেন্ট গুলা একেকটা খাস বিনুদুন! :D,0,celebrity
ভাইপুত কেন আছস?,0,celebrity
"অনেক ধন্যবাদ কেউ একজন কথা বলেছেন , আমরা লেখাপড়ার নামে একটা জেনারেশান এর বাল্যকাল নষ্ট করছি,এই অসুস্থ মানসিকতা পরিহার করুন এবং এদের boyhood টা ফেরত দিন।",0,celebrity
"Yes, we have noticed this shadashidhe.kotha page and tolerated so far because we thought it might be real fans. If you have any info about any page related to Zafar Sir's name and have suspicious activities, please let us know, we will try to take action as quickly as possible.",0,celebrity
স্যার মুখে মুখে তো বাঙালি বলে ফেনা তুলে ফেলান বাঙালিদের নববর্ষ কোনটা পহেলা জানুয়ারী? নাকি পহেলা বৈশাখ? আপনি যদি ইংরেজদেরটাও পালন করেন আবার বাঙালাও পালন করে তবে আরবিটা কেনো পালন করেননা? আপনি না কোরআন পড়েন? আপনি না নামাজ পড়েন?  চেতনা ব্যবসায়ী মুনাফিক নাম্বার ১ জাফর ইকবাল স্যার,0,celebrity
চোর মানেনা ধর্মের কাহিনী!!😜😂,0,celebrity
আপনাকে জ্ঞাণপাপী বললে কি আমার বিরোদ্ধে গুজবের অভিযোগ আসবে?,0,celebrity
আবারও তরুণেরা প্রত্যাখ্যান করবে জামায়াতকে,0,celebrity
স্যার না জেনেই এত বড় ছোট গল্প লিখছেন.... জানলে কি তা উপন্যাসে পরিণত করতেন????,0,celebrity
"শুনলাম স্যার নাকি বেহায়াপনাও করেছেন বিভিন্ন মেয়ের সাথে। বিশ্বাস করতে পারিনি তখন এত মহান একজন মানুষ বেহায়াপনা কিভাবে করবেন??  কোনভাবে নিজেকে স্থীর রাখতে পারলাম নাহ। তারপর শুনলাম তিনি নাকি নাস্তিক, ""ভুতের বাচ্চা সুলেমান ' একটা বই তিনি লিখেছেন।  এবং আরো কিছু বই ছিলো যেগুলা নাস্তিকতায় ভরপুর ছিলো।  তবুও আমার এত বড় মাপের একজন মানুষকে দেখে বিশ্বাস হয়নি তিনি এসব করবেন। চোখের সামনে পড়ে গেলো স্যারের বেহায়াপনার ফোটেজ। তাই যেই স্যার কে এত বিশ্বাস এবং মহান মনে করতাম, এখন আমার পক্ষ থেকে তার জন্য জুতো মারা ছাড়া আর কোন উপাই দেখছি নাহ। তবুও সর্বশেষ একটা কথা বলবো, স্যার সুস্থ হয়ে আমাদের মাঝে ফিরে আশুক।এই কামনাকরি। বাংলার মানুষ তাকে আরও চিনুক। দেখুক এবং বুঝুক।☺☺☺☺",0,celebrity
এতোদিন পরে আপনার ঘুন ভাঙলো এদিকে পোলাপাইন আপনার গায়েবি জানাজা পড়বে বলে তৈরি হচ্ছে।,0,celebrity
কিন্তু পশ্চিমা জগতের মিডিয়া বিবিসি কিংবা গুরুত্বপূর্ণ সাময়িকী দি ইকোনোমিস্ট এর মত সাপ্তাহিকী কিন্তু এখনো যথেষ্ট শিক্ষিত বা উদার হতে পারেনি। এই বালের কথা কই পাইছেন শুওর? রোজ রোজ বালের আলাপ পাড়বেন আর গালির চোদন খাইয়াও বালের আলাপ কেম্নে কি ছার?,0,celebrity
কাগু ঘুমে থাকে হুশ থাকে না!!😁😁একটু চেতনা মলম বিক্রি কইরবে,0,celebrity
একটা সময় অভ্যাসে পরিণত হয়ে যাবে। তখন সে আর নকল ছাড়া আর কিছুই করতে পারবেনা।,0,celebrity
"স্যার অাপনার গা‌য়েবানা জানাজার সকল অা‌য়োজন ইতিম‌ধ্যো সম্পন্ন হ‌য়ে গে‌ছে , এখন এসব ব‌লে অার লাভ হ‌বেনা সবাই হড় হড় ক‌রে ব‌মি ক‌রে দি‌বে",0,celebrity
বিকাশের যে সকল গ্রাহক এখনও Bkash App সাইন আপ করেন নাই। তাদের কে বিকাশের পক্ষ হতে ৫০ টাকা দেওয়া হচ্ছে। নিচের লিংক থেকে Bkash App সাইন আপ করে ৫০ নিয়ে নিন। https://app.bkash.com/sign-up?referralCode=1CL06ROO,0,celebrity
ছাত্রলীগের যে বাহিনী নৌকায় ভোট না দেওয়ায় এক চার সন্তানের জননী কে ধর্ষণ করেছে...আমি সেখানে আপনার অদৃশ্য সুশীল অথর্ব বুড়ো সুবিধাবাদী ছোট বিচিহীন লিঙ্গ দেখতে পাচ্ছি 🙂🙂🙂,0,celebrity
"দ্যাখো দেখি কান্ড,  দুষ্টুরা বলে কিনা স্যার নাকি ভন্ড!",0,celebrity
আপনার জানাজা হবেই হবে দাদু!,0,celebrity
স্যারের বউরে একবার ছাত্রলীগ দলাইমলাই করার পর তিনি প্রতিবাদে বৃষ্টিতে ভিজেছেন। পরে আবার তাদের মাথায় হাত রেখে দোয়াও করছেন। আগামীতে ছাত্রলীগের সেঞ্চুরি মানিকরা যদি স্যারকে রাস্তায় পেলে দোচেও তিনি পরদিন কলাম লেখবেন ছাত্রলীগের পাচা মারায় যে এত শান্তি! এত আরাম জানা ছিল না। আহ! কি সুন্দর বাথরুম হয়েছে আমার তা বলে ছাত্রদের আমি বুঝাতে পারবা?,0,celebrity
"অদ্ভূত সুন্দর একটি পরিকল্পণা বিষয়ে অপূর্ব এই লিখাটি সম্পর্কে ইংরেজি মন্তব্যগুলো দেখে একটা প্রবাদ মনে পড়লো ""সাত কান্ড রামায়ন পড়ে সীতা রামের মাসি"" :P এই আয়োজন টার উদ্যক্তাদের কাছে আমরা কৃতজ্ঞ থাকবো,আমার ছেলে পড়ে ইংলিশ মিডিয়ামে,পড়াশোনা বা কর্মজীবনে আন্তর্জাতিক ভাবে ইংরেজী ভাষার প্রয়োজন বুঝে তাঁকে এই মিডিয়ামে দেয়া,আমার ছেলের ছোট্টবেলার একটা প্রশ্ন ছিল...মা আমার ইংরেজীতে বানান ভুলে তুমি রাগ করোনা,বাংলা বানান ভুলে এতো রাগ করো কেন?আমি বলতাম বড় হলে বুঝতে পারবি নিজের ভাষায় ভুল করাটা কতটা লজ্জার,এখন সে ইংরেজীতে এ* পেলে ততটা খুশি হয়না যতটা হয় বাংলায় এ* পেলে, আমার আত্মবিশ্বাস ছিল যে,আমরা যদি বাংলা মিডিয়ামে পড়ে ইংরেজী শিখে থাকতে পারি তাহলে আমার বাচ্চা শুদ্ধ বাংলা শিখবেই,আজ আমার ছেলেটা ৯ম শ্রেণীতে পড়ে, আজ আমি জানি সেদিন আমি ভুল ছিলাম না| এটা আমাদের অভিভাবকদের দ্বায়িত্ব সন্তানদের শুরু থেকেই মাতৃভাষার প্রতি সচেতন করে তোলা| ",0,celebrity
আমার প্রচুর দুক্ক  একটা কমেন্ট ও পক্ষে দেখলাম না,0,celebrity
"""ফকিরা, আপ্নারে হাতুড়ির বাড়ি দেয়নের কাম"" কইতে মন চায়!  কিন্তু আফসোস... বলতেও পারিনা!",0,celebrity
"আমি জাফর স্যারের অন্ধ ভক্ত নই , অন্ধ আম্লীগ নই , লেখাটা পড়ে মনে হলো , এটা একটা নিরপেক্ষ পর্যালাচনা মুলক লেখা। উনি আসলে বিএনপির ইস্তেহার নিয়ে কোনো তির্যক কথা বলেন নাই , বিএনপির বন্ধুরা উনাকে গালাগাল করে কমেন্ট দেয়ার আগে একটু মনযোগ দিয়ে লেখাটা পুরোপুরি পড়ুন। একটি উন্নত বাংলাদেশের কথা চিন্তা করে ভোট দিন। মুক্তিযুদ্ধের বাংলাদেশের সমুন্নত রাখুন।",0,celebrity
"সামান্য literary term বুঝেনা,,, এটা আবার university র অধ্যাপক,,, এর কাছে ছাএরা কী শিখে,,, আমার ভাবতে লজ্জা হয়,,,,!!",0,celebrity
জাফর নাহ হি ইজ মির্জাফর 😜😜😂😂😂,0,celebrity
আমার কাছে কখনো আপ্নি আহামরি কিছুই ছিলেন না এখনো নাই😊  কিন্তু আমার অনেক ফ্রেন্ডদের আইডল হলেন আপ্নি সেই হিসেবে আপ্নার প্রতি সম্মানটুকু ছিলো কিন্তু এইটা পড়ার পর বামুনের কথা মনে পড়তেছে এ কেমন আইডল?🐸,0,celebrity
নির্বাচন নিয়ে একটা কলাম লিখুন স্যার।,0,celebrity
অনেক কিছু জানতে পারলাম স্যার,0,celebrity
ঐ মিয়া গর্তটা না আপনি খুঁড়ছিলেন? তা সেই গর্ত থেকে জামাত বেরোয় ক্যামনে ম্যান? দায়ী তো আপনি-ই! আহ্ হা রে দুঃখ!,0,celebrity
স্যার আপনার দীর্ঘায়ু কামনা করছি। প্রকৃত রাজাকার বাজে মন্তব্য করবেই,0,celebrity
জল ডাকে আগুনও টানে আমি পুড়ি মধ্যেখানে দুইদিকে দুই খন্ড হয়ে যাআই আবার যাইই না আ আ না জ্বালাই না নিভাই না জ্বাআআলাই না নিইইভাই 😪,0,celebrity
কমেন্ট পড়তে আসলাম,0,celebrity
স্যার আপনার সস্তা বৈজ্ঞানিক কল্পকাহিনী পড়তে পড়তে আপনার ফেবুতে পোস্ট গুলাও বৈজ্ঞানিক কল্পকাহিনী মনে হয়।।সাথে আরো মনে হয় এই পরিমান দালালি কেবল কল্প কাহিনীতেই সম্ভব :),0,celebrity
"যতটা সম্মান জাতি আপনাকে দিয়েছে,সত্যিকার অর্থে এতটা সম্মান পাওয়ার যোগ্য আপনি নন! সরি পেইজ টা আললাইক করতে ভুলে গেছিলাম!  এক্ষুনি করে দিচ্ছি😊",0,celebrity
You are our inspiration. Long live sir,0,celebrity
স্যার আপনি এগিয়ে যান।।মুক্তিযোদ্ধা পরিবার আছে আপনার সাথে।।,0,celebrity
"আহা বিনোদন,,",0,celebrity
"এখন আমি পপকর্ণ খাব, আর স্যারের লিখা পড়ব",0,celebrity
এদেশের বুদ্ধিজীবীরা কোন ব্যাপার না জেনে কত অশ্বডিম্ব পাড়তে পারেন এটা তার প্রকৃষ্ট উদাহরণ।,0,celebrity
"স্যার সিলেটে বাতাবী লেবুর চাষ কেমন হয়? একটু যদি বলতেন দয়া করে..😞  অনেকক্ষণ বিটিভি দেখলাম কিন্তু ওরা দিনাজপুরের লেবুর খবর দিচ্ছে, সিলেটের বাতাবী লেবু চাষের খবর জানা খুব দরকার।",0,celebrity
আমি এখন মদ খাবো! আর কমেন্ট পড়বো। 😑😑😑,0,celebrity
"সবাই ধীরে সুস্থে কমেন্ট করুন। উত্তেজিত হয়ে কমেন্ট করতে গিয়ে বানান ভুল করবেন না। আমরা কমেন্ট করতে আসি না, শুধুমাত্র পড়তে আসি। তাই এমন ভাবে কমেন্ট করুন, যাতে আমাদের পড়তে অসুবিধা না হয়।  অনুরোধক্রমেঃকমেন্টস রিডার এসোসিয়েশন অব বাংলাদেশ।",0,celebrity
বমি জাফরের কাছ থেকে চেতনার গল্প ছাড়া আর কি আশা করা যায়!! ওনি কখনও প্রতিনিধি হতে পারে না। ও। আপনিতো আবার কমেন্ট পড়েন না। কোদাল নিয়ে বিজি,0,celebrity
দেশদ্রোহী এবং ৭১ এর পরাজিত শক্তিদের কথায় কষ্ট পাবেন না। এরা এতো নিরিহ মানুষ হত্যা করেও তাদের সপ্ন পূরন করতে পারেনি তাই তাদের এতো কষ্ট আর রিয়েকশন।,0,celebrity
জাপর ষাঁড়কে মাসুদা ভাট্টি ওরফে রনির সাথে বিবাহ বন্ধনে আবদ্ধ করে দেওয়ার জন্য জননেত্রী দেশরত্ন মাদার অফ হিউম্যানিটির কাছে জোর দাবি জানাচ্ছি,0,celebrity
কোটা সংস্কারের দাবিতে সারা দেশে চলছে শিক্ষার্থীদের তীব্র আন্দোলন | পুলিশের সাথে দফায় দফায় সংঘর্ষ।,0,celebrity
সহমত ভাই :-),0,celebrity
"খুব খারাপ লাগলো, স্যার আপনার বিপদ শুনে।  আল্লাহর যেন আপনাকে তাড়া তাড়ি সুস্থ করিয়ে দেয়। সে শুভ কামনা রইল।",0,celebrity
আগুনে পুড়ে মরা অনেক কষ্ট স্যার।,0,celebrity
"সাব্বাস মুহিব খান সাব্বাস।  ইহা কোন কবিতা নহে, ইহা একটি বুলেট।  জাফর সাহেব, কই পালালেন ছাত্রগুলোর এ দুর্দিনে? আপনাকে তো কিশোর গড়ার সাধক বলেই সবাই চিনে!  গেলেন কোথায় সুলতানা মেম! চুপ কেন আজ দুঃসময়ে? এ্যামনে তো খুব চাঙ্গা দেখি দেশ-দরদীর চোঙ্গা লয়ে!  চুপ কেন মুনতাসির সাহেব! বিজ্ঞতা আজ চুপসে গেছে? এ্যামনে তো খুব টকশো মাতান জ্ঞান গরিমার কথার প্যাঁচে!  কবির সাহেব ঘুমান! নাকি চাপ বেশি মুরগির আড়তে? দেশেই ! নাকি 'তাওয়াফ' পালন ঘুরতে গেছেন ওই ভারতে?  মানবতার পাহারাদার মিজান সাহেব উধাও নাকি! চাকায় পিষে ছাত্র মরে, আপনি নিখোঁজ, কারণটা কী?  শোষকরাজের পক্ষ নিতে দক্ষ সবাই খুব তো দেখি সব চেতনার মালিক সেজে দাপিয়ে বেড়ান, আজ হলো কী!  আজকে সবাই নিরব কেন? প্রজন্ম টোপ গিললো না, তাই! প্রজন্মকে পথ ভুলাতে পথ হারালেন আজ নিজেরাই!  অত্যাচারীর ছত্রছায়ায় বুদ্ধিজীবির পোশাক পরে খুব তো লাফান , আজ কেন ঘুম! নিজের প্রভুর পতন ডরে?  বয়সগুণে শ্রদ্ধা করি নীতির বেলায় জানাই ঘৃণা ফটকাবাজী ছেড়ে দেখুন মানুষ হতে পারেন কি-না!  চামচা চ্যানেল, চুন্নীরা কই! তোরাই তো তেল মারতি বেশি তোদের তেলেই জোর পেয়েছে অত্যাচারীর পাষাণ পেশী  তোদের হলুদ পক্ষপাতে ন্যায়ের হাতে শিকল ওঠে আমজনতা জাগবে যখন সূঁই লাগাবে তোদের ঠোঁটে  শকুনরা সব আতঙ্কে আজ চড়ুই পাখির মারের ভয়ে দেশ ছেড়ে ভাগ- পড়বি মারা ক্ষিপ্ত প্রাণের এই বিজয়ে।",0,celebrity
স্যার তাবলীগে গেছিলো তাই  পোষ্ট দিতে দেরি হইছে   :-),0,celebrity
সালাম স্যার ♥♥♥,0,celebrity
"""""বাংলাদেশটার জন্মই হয়েছিল মুক্তিযুদ্ধ দিয়ে, তাই সেই আদর্শটা নিয়েই যদি রাজনীতি করা হয়, তাহলে নির্বাচন নিয়ে আমাদের ভেতর কোনো দুর্ভাবনা থাকবে না কোনো দুশ্চিন্তা থাকবে না।"""" লাল সালাম স্যার",0,celebrity
আপনি দয়া করে ঐ question টি যারা আমাদের দেশের মহামারি হাতে নাতে ধরিয়ে দেওয়ার পরেও নিলজেজর মত বলে যে আমাদের হাতে এ ধরনের কোন প্রমান নেই।তাদেরকে মেইল করুন।,0,celebrity
আপনি একজন মুসলিম ঘরে জন্ম নিয়ে একটা হিন্দুর জন্য দোয়া করলে?  যে কিনা ইসলাম কে নিয়ে কুটক্তি করে? দিক্কার জানাই এমন মসল মান দের.....,0,celebrity
স্যার আমারে মাফ কইরা দিয়েন আমি ভুলে আপনার গায়েবানা জানাযায় অংশ গ্রহণ করছি। ক্ষমা চাচ্ছি স্যারর।  এখন আমার খুব হড়হড় করে বমি হচ্ছে। বাঁচবো কিনা সন্দেহ।,0,celebrity
"স্যার কিছুই জানেন না, তাই অনেক কথা জানিয়ে দিলেন।",0,celebrity
"জানি না স্যার,এই কমেন্ট হয় তো আপনি দেখবেন না... তাও বলছি স্যার.. আপনার মত মানুষ আমাদের এই দেশে খুব বেশি দরকার.. আপনাকে আমরা অনেক ভালোবাসি..খুব যলদি সুস্থ হয়ে আমাদের মাঝে ফিরে আসুন স্যার.. আপনার সু স্বাস্থ্য  এবং দীর্ঘায়ু কামনায় আপনার এক ক্ষুদ্র ভক্ত💜",0,celebrity
"“হরতালের খবর ছাপা হলে দেশের মানুষের ক্ষতি হয়। স্কুল-কলেজে ছেলেমেয়েরা যেতে পারেন না, দিন-মজুরের সন্তানরা না খেয়ে থাকে, লোকজন যাতায়াত করতে পারে না, ব্যবসা নষ্ট হয় এবং এসবের সঙ্গে এখন যুক্ত হয়েছে মানুষকে পুড়িয়ে মারা! কাজেই যদি দেশের সব পত্রিকার সম্পাদক এবং সব টেলিভিশন চ্যানেলের মালিক বসে ঠিক করতেন যে, এখন থেকে তারা কবে হরতাল ডাকা হয়েছে সেই খবরটি প্রকাশ করবেন না। রাজনৈতিক দলগুলোকেই দায়িত্ব দেবেন, তাদের নিজেদের দায়িত্বে যেন সেই খবরটি প্রচার করতে হবে, তাহলে কেমন হতো?” তখন আইনশৃঙ্খলা বাহিনী বেশি অসতর্ক থাকত এবং সাধারণ জনগণ আরো বেশি অনিরাপদ হতো। কারণ যারা হরতাল ডাকে, তারা হরতাল ঠিকই ডাকতো এবং মানুষ মারা বন্ধ করতো না বরং বাড়াত। তাই আমরা চাই বি.এন.পি আন্দোলন করুক(যদি আন্দোলনের কোনো যুক্তি থাকে)কিন্তু সেটা মানুষ মেরে না, গঠনমূলক ভাবে জনমত তৈরী করে। সরকারেরও উচিৎ মানুষ মারা যেকোনো ভাবে বন্ধ করা, না পারলে ক্ষমতা ছেড়ে দেওয়া। কারণ জনগনের নিরাপত্তার দায়িত্ব সরকারের উপরেই থাকে, এর জন্যই তাদেরকে ক্ষমতায় আনা হইছে।",0,celebrity
আমি শিওর মুক্তিযুদ্ধে পাকিস্তান যদি জিততো তো আপনি আজ পাকিস্তানের পক্ষে ঠিক এভাবেই লিখতেন। স্যাড! 😰,0,celebrity
"এখন আমি কমেন্ট পড়ব ,চানাচুর খাব আর প্রচুর হাসব😆প্রচুর 🐸 তবে পোস্ট কিন্তু আমি পড়ব না 😂",0,celebrity
উনি আয়না দেখেন না।,0,celebrity
আমি কমেন্ট পড়তে আসছি।,0,celebrity
"আপনি বললেন,  ""বিশ্ববিদ্যালয়ের শিক্ষকদের এই দেশের ছেলেমেয়েদের জন্য বিন্দুমাত্র মায়া নেই""।  আপনিও তো একজন শিক্ষক, কোটা নিয়ে আপনি যা করলেন মনে হল মায়া গুলো সরবত গুলিয়ে দিয়ে দিয়েছেন!",0,celebrity
স্যার যা কয়েচেন মাইরী! হড়হড়িয়ে বমাতে ইচ্চা কচ্চে।,0,celebrity
আমি ভাবি আমার বাচ্চাকাচ্চা রা বলবে একটা দালাল কে চিনতে তোমাদের ২৫ বছর সময় লাগলো। আরিফ আজাদ,0,celebrity
আগে ভাবতাম বাংলাদেশের সকল শিক্ষিত মানুষেরা শুধু ফেজবুক চালায় কিন্তু কমেন্ট সেকশনে আসার পর আমার ধারনা সম্পূর্ণ বদলে গেল। এখন মনে হচ্ছে যেন  বাংলাদেশের সকল অশিক্ষিতরাই ফেজবুক চালায়।যেখানে স্যার এত সুন্দর করে নিউইয়র্ক এর নির্বাচন সম্পর্কে লিখেছেন এটা পড়ে স্যারকে ধন্যবাদ জানানোর বদলে উলটে গালাগাল দিচ্ছে। অপনি আগে এইরকম একজন লেখক হয়ে দেখান না।তারপর না হয় গালাগাল দিবেন বাজে বাজে কমেন্ট করারা আগে একাবারও ভেবে দেখেন না আপনি ওনার মতোও হতে পারেন কিনা। বাঙ্গালী কিছু পারুক আর না পারুক অন্যের নিন্দা ভালোই করতে পারে.....,0,celebrity
কিনতে হবে বইটা........😊,0,celebrity
বুঝলাম নাহ কমেন্টে শারের কিছু ভক্ত তাকে আস্তিক বানানোর পাইতারা করছে আবার কিছু ভক্ত তাকে নাস্তিক বানানোর পাইতারা করছে 😂 মগা পেলুম।,0,celebrity
"স্যার যতা সময়ে আলোচনা, আশা করি combined action হবে ।",0,celebrity
"জামাত শিবিরের পোলাপান আপনার প্রিয় ক্যম্পাসে আপনার স্ত্রীর শাড়িখুলে নিয়ে থাকে , কোন ছাত্রীকে ধর্ষন করে বা ধর্ষনের শতক পূরন করে থাকে , কোন অপকর্ম করে থাকে , আপনার নিকট চাদাবাজি করে থাকে অথবা টেন্ডারবাজি করে থাকে তা হলে অবশ্যই তাদেরকে পরিহার করা আমাদের দায়িত্বের মধ্যে পরে তাই নয় কি স্যার ?? জানাবেন দয়াকরে ।",0,celebrity
zafar iqbal faltu luk,0,celebrity
জাফর ইকবাল একটি দীপশিখা। একটি চেতনা। এটা নিভবে না।,0,celebrity
আপনার ভিসি হওয়ার স্বপ্ন পূরণ হউক!,0,celebrity
"কিন্তু যেদিন আমি আবিষ্কার করেছি, ন্যায় আর অন্যায়ের মাঝখানেও কেউ কেউ নিরপেক্ষ হতে শুরু করেছেন, সেদিন থেকে এই শব্দটিকে আমি সন্দেহ করতে শুরু করেছি'- ঠিক কিছুদিনের মাঝেই এই সব নিরপেক্ষরা তাদের আসল চেহারা দেখিয়ে দিয়েছে, খুব হতাশ লাগছিল, সব সময়ের মত স্যারের লেখা পড়ে আবার সান্ত্বনা পাচ্ছি, কিন্তু আজকাল সত্যি এসব ভয়ঙ্কর বিশ্বাসীদের দেখে হতাশ হয়ে যাচ্ছি।",0,celebrity
মোল্লাদের বিরুদ্ধে লিখার skill = super fine নিরাপদ রাস্তার পক্ষে লিখার skill= Lmfao 😀,0,celebrity
দেখো দিলদার এর মতো জোক্স বলছে লোকটা।,0,celebrity
"জাফর ইকবাল যেমন জ্ঞানী, তেমনি জাফর ইকবাল এর পোস্টে এপিক কমেন্টকারী লোকগুলোও প্রচুর জ্ঞানী।",0,celebrity
"""আমি বলছি না আমাকে মুক্তিযোদ্ধা বলতেই হবে,আমি চাই কেউ একজন আমার জন্য একটি কোদাল নিয়ে আসুক, আমি ট্রেঞ্চ খুড়তে পারি কিনা তা প্রমাণ করার জন্য। বাচ্চাদের মুক্তিযুদ্ধের গল্প বলতে বলতে আমি এখন ক্লান্ত । আমি বলছি না আমাকে মুক্তিযোদ্ধা বলতেই হবে,আমি চাই কেউ আমার কাছে চেতনার গল্প শুনতে চাক, আমি কতটা আঘাত পেয়েছি জিজ্ঞাসা করুক, চেতনার সঙ্গী না হোক, কেউ অন্তত আমাকে জিজ্ঞাসা করুক, ""তোমার ড্রোন থাকার পরেও,ট্রেঞ্চ খুড়তে কোদাল লেগেছিল কেন?""",0,celebrity
"আচ্ছা স্যার,আপনার মোচ গুলি উপজাতিদের বালের মতো কেন?",0,celebrity
আপনার লেখা সবটুকু পড়ার দরকার হয়নি!! আপনি হলেন সুবিধা বাদী!! যোদ্ধ করতে না গিয়ে ও আপনি মুক্তি যুদ্ধা?? কালা মুতিয়া যখন আন্দোলনকারী শিক্ষাথীতের রাজাকারের বাচ্ছা বলেছিলো তখন আপনার যুক্তি কোথায় ছিল!!?? প্রশ্ন উঠে নাই মনে?? রাজাকারদের আমরা ঘূনা করি!! আর মুতিয়া সংসদে কি বললো প্রশ্ন হয় মনে?? এটা নিয়ে কোন দিন আপনার মনে প্রশ্ন উঠবে না??,0,celebrity
"কেউ বুঝায়ে দেন, অত ধৈর্য্য নাই পড়ার। আমি আবার কোচিং এর স্যারের কাছে পড়ি তো!  নিজে নিজে কিছু বুঝিনা।",0,celebrity
"আপনাকে স্যার বলতে আমার লজ্জা হয়, আপনি যতই সরকারের সমালচনা করেন না কেনো সরকার আপনাকে গ্রেফতার করবে না।কেননা আপনাকে আজকে কুতকুতালে আপনি কালকে হাসেন.💩💩💩",0,celebrity
ধোঁকা দিয়ে যদি ছাত্রদের দমানো যেতো তাহলে বাংলাদেশ স্বাধীন হতো না।  আইনজ্ঞ ও সংবিধান বিশেষজ্ঞ ডঃ তুহিন মালিক,0,celebrity
সিলেট শহরটা কবুতরের জন্য বিখ্যাত।  শাহজালাল মাজারে আছে কিছু জালালি কবুতর।  শাহজালাল বিশ্ববিদ্যালয়ে আছে একটা দালালি কবুতর।  Arif Adnan bai,0,celebrity
ও আল্লাহ।। সাইন্স ফিকশন সত্যি হয়া গেসে।শনিগ্রহ থেকে এলিয়েন উনাকে নিয়ে গেসে।এখন ইনার রুপ ধরে এলিয়েন বসে আসে।,0,celebrity
"Tahazzot Hossain, ৭১ এ স্যারের বাবা মুক্তিযুদ্ধে শহীদ হয়েছেন। ৭১ এ আমার বাবা এবং ২ মামা মুক্তিযুদ্ধ করেছেন? আপনার ফ্যামিলির মুক্তিযুদ্ধের ইতিহাসটা বলেন শুনি!",0,celebrity
"পোস্টটা কেনো দিলেন স্যার। এরা আপনার আবেগ এবং অবস্থান কখনো বুঝবেনা। আপনি আমাদের কাছে আদর্শবান ছিলেন, আছেন, থাকবেন। বাই দ্য ওয়ে, ওয়েলকাম টু আর্থ! 🐸🐸",0,celebrity
মনু তুমি বেঁচে আছ আমি ত ভেবেছিলাম ডুমুরের ফুল দিয়ে তোমাকে সম্মান জানাবো :3 তুমি আর কপালে রাখলা কই :3 সম্মান তা জানাতে পারলাম না বিদায় পিতিবি :3,0,celebrity
"স্যার, আমরা মূর্খ জাতি। আপনাকে সম্মান জানানোর মত জ্ঞান এখনো আমাদের হয়নি। ক্ষমা করে দেবেন স্যার।",0,celebrity
মানুষ এত নিচে নামতে পারে ভাবা যায় না। সর্বনিম্ন স্তরের দাদাল👿👿,0,celebrity
কিছু বলার নেই! দেশে 4G এলেও স্যার এখনো Taletalk এর 1G কাকুদের নেট চালান তাই তার কাছে আবেগ/বিবেক সৃষ্টি হতে সময় বেশি লেগেছে হতাসা সবই হতাসা 😭 😭 😭,0,celebrity
এই কে আছিস ? এই জাফর মিয়ার জন্যে এক্টা মন্ত্রীর পদ সাজায়া রাইখা দে। হ্লালায় ইনিয়ে বিনিয়ে সেটাই বুঝাইতেছে।,0,celebrity
"আমার মেয়ের বয়স ৬ বছর.....  pls,  স্যার কিছু একটা করুন... নিয়মটা পাল্টে দিন.....  মেয়েকে যেনো psc/ jsc অত্যাচার  না পেতে হয়।।",0,celebrity
স্যার আমরা আছি- আপনি আছেন আমাদের সাথে! এই পৃথিবীর মানুষজন আপনাকে খুব ভালোবাসে- আপনি দ্রুতই সুস্থ হয়ে ফিরবেন!,0,celebrity
দুইজন লেখকের মা (নিজেও লেখক) তার বইতে লিখেছেন যে মুক্তিযোদ্ধারা নাকি তার হাজবেন্ডকে হত্যা করে তাহলে বুঝা যাচ্ছে তিনি মুক্তিযোদ্ধার সন্তান,0,celebrity
"কিছু মানুষ আছে যাদের ভালোমন্দ বিবেচনা করার ক্ষমতা নেই, যেখানেসেখানে হা হা রিয়েক্ট দেয়।  আর একদল আছে  যাদের বড় পোস্ট পড়ার ধৈর্য মোটেও নেই, তিন লাইনের কমেন্ট পড়ায় খুব পটু আর ভুল বানানে উত্তর দিতে আরও বেশি পটু।",0,celebrity
"ভংগির মাত হুন, পত্রিকা পড়তে ডরায়। দুই তিনবারে একটা নিউজ পরইন। এখন আর ইতা খায় না।",0,celebrity
শুভ অপরাহ্ন!,0,celebrity
এরা কখনো মানুষ কে মানুষের মূল্য দিতে পারে নাই. Ak ta কথা বললো না. এতো কিছু হলো 9 দিনে. মুখে আঙুল দিয়ে বসে ছিলেন. আজ হঠাৎ করে তার হৃদয় রক্তপাত হতে লাগলো.,0,celebrity
অত্যন্ত মূল্যবান উপদেশ|,0,celebrity
নতুন বছরে নির্বাচনী গণধর্ষণকে আপনি অভিনন্দন জানাবেন কি?,0,celebrity
"লেখা যদি মাথার উপ্রে দিয়ে যায় , কমেন্ট গুলো ছাগ্লা টাইপেরই হবে।। তাতে কার কি??",0,celebrity
স্যার বাঙ্গালী আপনার মুল্য দিতে পারবে না!  আপনি কেন দু দিন পর পর গর্ত থেকে উঠে এসে তেল মালিশ করেন?  প্লিজ আপনি উগান্ডা চলে যান!  ওখানে আপনার মুল্যায়ন করা হবে যথাযথ,0,celebrity
চুর শ্লা,0,celebrity
"বন্ধু, আমি তোমার ফেসবুক সেলিব্রিটি।  একটা কমেন্ট করতে আসছিলাম। কিন্তু বিয়াদব বদ শুয়োর গুলা তোমাকে যে গালি দিচ্ছে। ওদের গালি দেখে আমি ভাবতেছি আমি যদি তোমাকে গালি না দি তাহলে ওরা কি মনে করবে!  তাই তোমাকে একটা গালি দিচ্ছি, বন্ধু হিসেবে ক্ষমা করে দিওহহ।   গালি টা হচ্ছে ""জাফর""।",0,celebrity
জানাজা পরানোর পর উনি কবর থেকে উঠে আসলেন নাকি???????? !!!!!!!,0,celebrity
"আমরা আছি আপনার সাথে,  এগিয়ে যান Sir.......",0,celebrity
"আপনাকে কিছু জানতে হবে না, ঘটনা ঘটার এতো দিন পর কেন মুখ খুলেন?যেন সরকার আপনার উপর রাগ না করে তাই!রিমান্ডের ভয়ে চুপ করে থাকা মানুষ আমাদের দরকার নাই।আজ যদি আপনার বড় ভাই থাকতেন তবে অনেক আগেই আমাদের পাশে দাড়াতেন।😒😒😒",0,celebrity
পাবলিক পারসেফসন দেখতে আসলাম। যা বোঝার বুঝলাম। দালালি ও  অর্বাচীনের স্থান বাংলার মাটিতে হবে না।,0,celebrity
"আমরাও সেটা প্রত্যাশা করি,কিন্তু প্রতিনিয়ত ধর্ষিত হচ্ছে আমাদের যে মা-বোনগুলো তাদের নিয়ে আপনাদের কি কোন চিন্তা হয়,এধরনের অপকর্ম থেকে পরিত্রান কিভাবে পাওয়া যায় সেই বিষয়ে আপনার মত ব্যক্তিবর্গের কি কোন পদক্ষেপ আছে?",0,celebrity
"@Muhammed Jafor Iqbal sir আপনার কাছ থেকে এই পথভ্রষ্ট তরুন প্রজন্ম বিজ্ঞান বিষয়ক যে শিক্ষা পেয়েছে তা কিন্তু অন্যের ভূলকে সংশোধন করতে শিখিয়েছে, নির্লজ্জ্ব রাজনৈতিক সমালোচনা করে আমাদের জাতীয় ব্যক্তিত্ত্ব স্যার জাফর ইকবালকে হেয় করার অধিকার আপনার আছে কিনা নিজেকে প্রশ্ন করুন!",0,celebrity
থ্যাংকস সৃজন। এসব কমেন্টের প্রোটেস্ট দরকার আছে।,0,celebrity
"আবারও জানি না, পারি না, বুঝি না,  করি না, ধরি না, না, না, না এভাবে হতে পারে না....... উহ বিকট.....",0,celebrity
"Spellling Bee দেখার পর বাংলা নিয়ে আক্ষেপ হয়েছিল! যাক,উদ্যোগ অন্তত নেয়া হল :) হার্ডকোর বিজ্ঞান নিয়ে লিখিয়ে মানুষটা বাংলা ভাষার সঠিক ব্যাবহার নিয়ে লিখলেন,নতুনভাবে আরেকবার আবিষ্কার করলাম স্যার আপনাকে!",0,celebrity
স্যার আমি গ্রামের একটা স্কুলে বিঞ্জান বিভাগে দশম শ্রেনিতে পড়ি....আমি আপনার মত জীবনে সফল একজন ব্যক্তি হতে চাই... পারব কিনা জানি না...তবে আপনার কাছে আমার অনুরোধ আপনি আমার মত উচ্চাকাঙ্খীদের জন্য একটা বই লিখবেন কিভাবে আমরা জীবনে সফল হতে পারি...প্লিজ আধীর আগ্রহ নি আপনার বইয়ে অপেক্ষাতে থাকব...,0,celebrity
আপনার কাছে পাঠকদের অনুরোধ আপনি কার কাছে দোয়া করেছিলেন পাঠকরা জানতে চায়।বিশেষ অনুরোধ করছি একটু জানাবেন।,0,celebrity
ডঃ জাফর ইকবাল একজন বিদগ্ধ পন্ডিত ব্যক্তি তবে তার আচরণ স্বার্থপরের মত। একদিকে দেখেন। (ব্যক্তিগত মতামত)।,0,celebrity
কম দামি মদ খাইলে  এইরকম ই জনে,0,celebrity
"মীর জাফর--------- ইকবাল, তুমি মানুষের মত মানুষ হবে কবে????",0,celebrity
"রচনা পড়ার সময় এখন আর নাই স্যার , সবাই এখন রাস্তায়",0,celebrity
সমস্ত রাজাকার সন্তান দের চিনে রাখুন এ পেজ থেকে|,0,celebrity
আপনাকে এবং ছবি প্রদানকারীকে শুভেচ্ছা।,0,celebrity
"যারা স্যার কে নিয়ে বাজে কমেন্ট করে,  তারা আসলে কোয়ার ব্যাঙের মত।   তারা ছোট সেই কোয়াটা কে তাদের পৃথিবী ভাবে। নিজেকে সব জান্তা ভাবে। যারা আসলে এসব করে তারা এটাই প্রমান করে যে তারা কিছুই জানে না",0,celebrity
এই পরীক্ষা বাতিল হোক,0,celebrity
স্যার মনে হয় আজ রাতে টি২০ ম্যাচ খেলে পোষ্টটা করেছে।,0,celebrity
হর হর করে আপনার উপরে বমি করে দিলাম :-),0,celebrity
আল্লাহ আপনাকে হেফাজত করুক স্যার।  আমরা চাই আপনি পৃথিবীর বুকে বিষ্ময়কর হয়ে থাকুন। হুমায়ুন আহমেদ স্যার কে মন থেকে ভালেবাসি। তার লেখা বই পড়লে আজো নিজের অজান্তে কেঁদে ফেলি। আল্লাহ উনাকে জান্নাত বসিব করুক আমিন।,0,celebrity
"এক সময়ের গভীর শ্রদ্ধা যখন ধীরে ধীরে অশ্রদ্ধায় রূপান্তরিত হয়, অবশ্যই তার একটা তাৎপর্য্য পূর্ন ঘটনা প্রবাহ থাকে।  আপনি সেই ব্যাক্তি যে নিজের বিবেক কে বিকিয়ে দিয়ে অজস্র মানুষের অশ্রদ্ধায় রূপান্তরিত একজন কলঙ্কিত মানুষ। যে পারে শুধু প্রভুর সন্তুষ্টির জন্য ল্যাজ নারিয়ে যেতে। আপনার মতো কিছু পাচাটা লোক শিক্ষকতায় আছেন বলেই আজ জাতির এই করুন দশা। ধীক্কার জানাই আপনার এই নীচুতা কে, ধীক।",0,celebrity
সে মনে হয় হিন্দু ওনা মুসলমান ওনা সে আওয়ামীলীগ।,0,celebrity
"এই জাফর মুজিবের বীর্যের সন্তান,  কিছু বল........",0,celebrity
"জানতে চাই, স্যারকে বাংলা উইকিপিডিয়া তে কেন মৃত দেখায়?  =======================   জ্যুতসই বাংলা উইকিপিডিয়া 😂👌  সেখানে নাকি চেতনা ব্যবসায়ী জীবিত জাফহহহহহহহড়ড়ড়ড়ড় ইলবালবালবাললল সাড়কে নাকি মৃত দেখাচ্ছে...😉  সব্বাই ১মিনিট নিরবতা পালন করি✌️ ছ্যারকে অনেক মিস করব। ভালো থাকবেন পরপারে...😂 Be Positive😜   শিক্ষাবিদ মুহাম্মদ জাফর ইকবালকে মৃত দেখাচ্ছে বাংলা উইকিপিডিয়া। সেখানে তাঁর জন্ম তারিখ লেখা রয়েছে ২৩ ডিসেম্বর, ১৯৫২। পাশে মৃত্যু সন ২৯ জুলাই, ২০১৮ লেখা রয়েছে। যদিও তিনি এখনো বেঁচে আছেন। ২ আগস্ট ১১টা ৩৪ মিনিটে এ তথ্য সংযোজন করা হয়। তবে ইংরেজি উইকিপিডিয়াতে অবশ্য এমন কোন তথ্য নেই।",0,celebrity
"এরা আসলে মুক্তিযুদ্ধ বিরুদী, না হলে এতক্ষনে মাত্র এই কইটা কমেন্ট করে? আমার এত টাকা দামের মুড়ি সব রয়ে গেলো। ব্যাট কমেন্ট পড়া শেষ। তোমার কাছে বিচার দিলাম।।",0,celebrity
"আমার প্রাণপ্রিয় মরহুম দুলাভাইয়ের সাথে শুধুমাত্র আপনাকে নিয়েই আমার আরগুমেন্ট হত উনি বলতেন আপনি ভুয়া আর আমি বলতাম না আপনি ভুয়া নয় আজ সব সন্দেহ দূর হল আফসোস দুলাভাই আজ বেঁচে নেই।। দেশের মানুষ ভোট দিতে পারল না এটা নিয়ে একটা কথাও বললেন না, এত ছোট কলিজা নিয়ে বেঁচে আছেন কেমনে! অদবোদ",0,celebrity
"আহমেদ মুরশিদ্দিন, তা ভাইয়া আপনি কার জন্ম অডিয়েন্স জানতে চায়। সেসব রাজাকারের বাচ্চারা না হয় ভূল করলো। আপনি মুক্তিযোদ্ধার বাচ্চাটা কি করলেন?   ভাইয়া ব্যবহার ভাল করতে পয়সা লাগে না।  সেই কবিতার পংতিদ্বয় স্মরিয়ে দেয় মোরেঃ কুকুরের কাজ কুকুর করেছে, তাই বলে আপনিও কি?",0,celebrity
"জনাব জাফর স্যার ১৯৭১ সালে ১৯ বছরের তাগড়া যুবক থাকা সত্বেও মহান মুক্তিযুদ্ধে অংশগ্রহণ করেননি। #সুতরাং এখানে ঘাপলা আছে। . কথিত আছে তিনি তখন পিরোজপুরের ছারছীনা মাদ্রাসার আশেপাশে লুকিয়ে ছিলেন। উল্লেখ্য যে, এখানেই দক্ষিণবঙ্গের অন্যতম বড় রাজাকার ক্যাম্পের অবস্থান ছিল। সুতরাং এখানে ঘাপলা অবশ্যই আছে। . জনাব হুমায়ুন আহমেদের মতে তার নানা রাজাকার ছিলেন এবং স্বাধীনতা পরবর্তী সময়ে মুক্তিযোদ্ধারা তাকে পিটিয়ে মেরে ফেলে। সুতরাং এখানে ঘাপলা আছে। . একটা বই পড়েছিলাম, যেখানে মুক্তিযুদ্ধকালীন সময়ে জনাব জাফর ইকবালের বাবার কর্মকাণ্ড সম্পর্কে প্রশ্ন তোলা হয়েছে। সুতরাং এখানে ঘাপলা থাকলেও থাকতে পারে। . তার লিখিত বইগুলোকে নিয়ে ইংলিশ মুভিবাজ জেনারেশন কপি-পেস্ট বলে প্রশ্ন তুলেছেন। সুতরাং এখানে ঘাপলা আছে। . এত ঘাপলার মাঝে তিনি যে ভাব নিয়ে জাতির সামনে ভাব দেখান এবং চেতনা প্রকাশ করেন; ভাবলেই আমার শরীর ঘীণঘীণ করে, আর তার দিকে দিতে ইচ্ছে করে, ও  য়া  ক  থু.........",0,celebrity
স্যারের আস্তে আস্তে হুশ ফিরে আসতেছে।,0,celebrity
"এতক্ষণ পর্যন্ত বিশ্বের বিভিন্ন দেশের যতজন রাষ্ট্রনায়কের নাম বললেন তারা সবাই নিজেদের দেশে একচেটিয়া জনপ্রিয় ছিল। তারা কেউ দেশের স্বাধীনতা বিকিয়ে প্রতিবেশি প্রভাবশালী রাষ্ট্রের সাথে গোলামি চুক্তি করেন নি। মানুষের বাক-স্বাধীনতা কেড়ে নেননি। তারা কেউ গনতন্ত্র হত্যা করে একদলীয় স্বৈরাচারী শাসন চালু করেন নি। বহির্বিশ্বের সেই রাষ্ট্রপ্রধানরা কেউ রক্ষীবাহিনীর মত ঘাতকবাহিনী গড়ে তুলে ত্রিশ হাজার বিরোধী মতাবলম্বী নেতাকর্মীদের গুম-খুন করেননি। তাদের শাসনামলে অবাধ লুটপাটের দরুন সৃষ্ট দুর্ভিক্ষে ১৫ লাখ মানুষকে মরতে হয়নি। শেখ মুজিব নিহত হবার পর ক্ষমতার কামড়াকামড়ি নিয়ে তার দলের সবাই ব্যস্ত হয়ে পড়ে, কেউ পাশে দাঁড়ায় নি। সেদিন যারা তার দলের লোক হয়ে বেঈমানী করেছে আজ তারা সবাই এমপি-মন্ত্রী। শেখ মুজিব নিহত হবার পর হত্যাকারীদের ইনডেমনিটি দিয়েছে স্বয়ং তারই বিশ্বস্ত সহচর খন্দকার মোস্তাকের নেতৃত্বাধীন আওয়ামী লীগ সরকার। 'স্বাধীনতার ঘোষক কে? জিয়াউর রহমান, নাকি শেখ মুজিবুর রহমান?’- এ প্রশ্নের উত্তর দেবার মত প্রজ্ঞা আপনার মত দলকানা বুদ্ধিজীবীর নাই। স্বাধীনতার ঘোষক কে তা জানতে ১৯৭১ সালের মুক্তিযোদ্ধা, ৭৫ সালের বিমানবাহিনীর প্রধান, আওয়ামী লীগ সরকারের সাবেক পরিকল্পনামন্ত্রী এ.কে. খন্দকারের ""১৯৭১: ভেতরে-বাইরে"" বইয়ের ৫১-৬৩ পৃষ্ঠা পর্যন্ত পড়ে দেখবেন। শেখ মুজিবের নাম ইতিহাস থেকে কেউ মুছে ফেলতে চায় নি বরং মুজিবকন্যা হাসিনা গনতন্ত্রবিনাশী নির্বাচনের মাধ্যমে দেশের ক্ষমতা দখলে রেখে মহান মুক্তিযুদ্ধে জিয়াউর রহমান, তাজউদ্দিন আহমদ, জেনারেল ওসমানী, সেক্টর কমান্ডারগন ও দেশের অপামর জনসাধারনের বীরোচিত অবদান অস্বীকার করে মুক্তিযুদ্ধের সব ক্রেডিট ব্যক্তি মুজিবকে দিয়ে দিয়েছে। যার যা অবদান তা স্বীকার করুন। একাত্তরে দেশের অপামর জনসাধারন সবাই মুক্তিযুদ্ধ করেছে। কারো একক নৈপুণ্যে দেশ স্বাধীন হয়নি। ইতিহাস বিকৃত করা বন্ধ করুন। নইলে এই ইতিহাস একদিন প্রতিশোধ নেবে। বাংলাদেশের জন্য সবচেয়ে বড় দুর্ভাগ্যের বিষয় হলো কি জানেন, আপনার মত দলকানা চাটুকার কিছু পাচাটা বুদ্ধিজীবী জন্ম দেয়া। শাসকগোষ্ঠির নির্লজ্জ চামচামি করে আপনার সম্মান কর্পূরের মত উড়ে গেছে। আপনি পঁচে গেছেন। অনুগ্রহ করে মুখ বন্ধ রাখুন। আপনি যতই কথা বলবেন, দুর্গন্ধ ছড়াবে।",0,celebrity
ওহ স্যার বেচে আছেন তাহলে।একটা মৃত মানুষ ৩-৪  দিন পরে করব থেকে উঠে এসে কথা বললো। না মানে মৃত বলতে গতকাল আপনার গায়েবী জানাজা পড়ে দাফন-কাফনের কাজ সম্পন্ন করেছিলাম তো তাই হুট করে আপনাকে দেখে স্তম্ভিত হলাম।😂😀বাই দা ওয়ে আপনি তো বাংলাদেশের শিশু এম্বাসেডর ও বটে কি কি প্ল্যানিং করলেন এই কয়েকদিনে ঘরে বসে???    জাতি জানতে চায়☺☺,0,celebrity
স্যার দল করেন ঠিকি! কিন্তু দলকানা না!😊,0,celebrity
"আপনাকে বেঁচে থাকতে হবে, আমাদের জন্য, শত শত তরুণের জন্য, কারণ আপনার চোখে আমরা আবার পৃথিবী দেখতে চাই। <3 <3 <3",0,celebrity
"স্যার,  আজ আবারো একটা যুদ্ধ এর প্রয়োজন দেখি।  পাক সাফ হয়েসে কিন্তু রাজাকার কুত্তারা বে ছে আসে",0,celebrity
স্যার আপনাকে আর ভালোবাসি না স্যার আপনাকে ঘৃণা ও করি । কেমন যেনো আপনাকে ঘৃণা করার ইচ্ছাও হয় না । সবাই যখন নাস্তিক বলে আপনাকে গালি দিত তখন আপনার প্রেমে আমি মজিত আপনার গল্প পড়ে রোমাঞ্চিত হতাম। কিন্তু স্যার সত্যি আপনি এতো বড় মাপের মানুষ হয়েও এতো ভালোবাসা পাওয়ার যোগ্য না । সর‍্যি স্যার আপনাকে ঘৃণা করতেও রুচিতে বাদে এই নিন্ম ক্ষুদ্র আমারো  ।,0,celebrity
ভন্ড হালা 😒,0,celebrity
এবার সত্যি অনশন করব। গাঁজার দাম না বাড়লে দেশে থাকা যাবেনা। এরা ফেসবুক খেয়ে গাঁজা দিবে।,0,celebrity
পরে পড়ব এত লম্বা লিখাটা,0,celebrity
"গতকাল রাতে আমি ঘুমিয়ে ছিলাম।মাবাবা নিচের ফ্লোরে, আমি একা উপরের ফ্লোরে।বড় ভাইয়া বাসায় না থাকায় বাড়িতে আমরা মাত্র এই তিনটি প্রাণি। রাতের বেলা হঠাত দেখি, একটা বাচ্চা হেলে দুলে আমার দিকে আসছে।কুচকুচে কালো, তেল চিকচিক গাল, কান দুটো একটু খাড়াখাড়া, আর চোখ দুটো একেবারে কোঠরের ভেতরে।চাহুনীতে ঐদ্ধত্য ভাব।এক পা রাস্তার বাম পাশে দিচ্ছে আরেক পা দিচ্ছে ডান পাশে।এভাবে হেঁটে হেঁটে ও আমার দিকে এগিয়ে আসছিলো।আমি এই ফাঁকে চিন্তা করতে থাকলাম বাচ্চাটা কোন জাতির হতে পারে? ভূত, প্রেত, পরী, অথবা অন্যকিছু।কিন্তু না কোনো দিকেই ধারণাটা প্রবল হলো না।ভাবতে ভাবতে একটা সময় ও আমার সামনে এসে দাঁড়িয়ে পড়লো।আমার দিকে তাকিয়ে ফিক করে হেসে দিলো। এই হাসিতে এমন একটা উৎকট গন্ধ বেরুলো যে, গন্ধে আমার নাক বন্ধ হয়ে যাওয়ার উপক্রম হয়েছিলো।ওর দাঁত হলুদ,মুখ ময়লাযুক্ত।আমি জিজ্ঞেসা করলাম, নাম কী তোমার? বললো, জাফর ইকবাল।আমার তো চোখ কপালে।আবার জিজ্ঞেসা করলাম, তুমি কোন জাতির? বললো শয়তান জাতির।আমি শয়তানের বাচ্চা জাফর ইকবাল।এটা শুনে আমার খুবই খারাপ লাগলো।বললাম,তুমি এমন নাম কেনো রেখেছো পাল্টে ফেলো! ও বললো, আমার মা রেখেছে।তাই আমি পাল্টাতে পারবো না।আমি কিংকর্তব্যবিমূড়",0,celebrity
"স্যারের লেখা কিছু বই পড়ে যতটা-না স্যার সম্পর্কে জেনেছি, তার চেয়ে হাজার গুণ বেশি জেনেছি এই কমেন্টস বক্সে এসে..... হাউ ফানি.....😜😜",0,celebrity
"স্যার, গণজাগরণ মঞ্চের উপস্থিতির মতো আপনার উপস্থিতি কাম্য করি এই অসহায় বাচ্চাগুলোর মাঝে। আপনি যদি বাচ্চাগুলোকে এসে একটু সাহস দেন, তাহলে আপনার সাহসও কমবেনা, বরং বাড়বে। আপনাকে বিভিন্ন সময় কাছে থেকে দেখার সৌভাগ্য হয়েছে আমার। বারবারই আপনাকে বেশ প্রভাবান্বিত করে ফেলা মানুষদের মতোই লেগেছে। আপনি নিজেও আমেরিকায় অনেক বছর ছিলেন। সেখানকার আইন কানুন আপনি অনেক ভালো জানেন। আপনি কি চাননা, এই দেশটাও ৪৭ বছরে এমন একটা যৌক্তিক আন্দোলনের মাধ্যমে অন্তত কিছুটা আমেরিকার মতোন হোক? দেশের প্রতি আপনার অনেক ভালোবাসার কথা শুনেছি ও পড়েছি। এইসব বাচ্চাদের জন্যইতো আপনি আজ এতো ফেমাস। এইসব বাচ্চারাই আপনার বই কিনে কিনে পড়ে। আপনি এইসব বাচ্চাদের কাছেই আইডল হয়ে ওঠেন। আপনার কি মনে হয়না, এইসব বাচ্চাদের পাশে দাঁড়ানো উচিত? আপনি জ্ঞানী মানুষ। রাজনৈতিকভাবে আপনি হয়তো দেশের শাসকদের ভয় পান। আপনি রাস্তায় নেমে আসুন, দেখবেন সব ভয় কেঁটে গেছে। আপনার সামনে পিছনে থাকবে লাখ লাখ কিশোর-কিশোরী!",0,celebrity
এই উদ্যোগ অনেক উপকারে আসবে।ক্ষুদ্র ক্ষুদ্র আবিষ্কার এক সময় বৃহৎ আকার রূপ ধারণ করবে।,0,celebrity
"অসাধারণ, প্রভাবিত হবার মতোই লেখনী।তবে,চাঁদের মতো স্যর 'দেরও আছে(ভীরুতা?)।",0,celebrity
"এগিয়ে আসার কারেনই তো পাঁচতলা থেকে ফেলে দেয় নবজাতককে   আজ দেখলাম সেই তরুণী আটক হইছে যিনি চাচার সঙ্গে অবৈধ যৌন লিলায় মেতে উঠছিল, শেস পর্যন্ত নিজে বাঁচতে পাঁচতলা থেকে নবজাতককে ফেলে দেয়, এরা কিন্তু এই জাফর ষাড়ের অনুপ্রাণিত।  https://www.bd24live.com/bangla/article/1558850230/205804/index.html",0,celebrity
থু থু!,0,celebrity
"যারা  কমেন্ট  করতেছে জাফর স্যার মারা গেলে খুশি হইত।তারা তো আহামমক শফীরে পছনদ করে। যে কিনাবলে ।মেয়ে মানুষ  তেতুলের মতো।তেঁতুল দেখলে যেমন জিববায় পানি আসে  তো         মনি  মেয়ে মানুষ দেখলে নাকি ,,।।।।।  ।।। ।ঠিক থাকতে  পারে না।",0,celebrity
"একটু মনোযোগ দিয়ে জোকসটা পড়বেন..  টিচারছাত্রকে প্রশ্ন করলো টিচার: এই আবুলবলতো জনক কয় প্রকার?  ( ছাত্র এত সোজা প্রশ্নশুনে দাঁত কেলিয়ে ফটাফট দাড়িয়ে উত্তর দিল )  ছাত্র:স্যার জনক হইলো ২ প্রকার৷ একটা হইলো 'জাতিরজনক' আর আরেকটা হইলো 'আশঙ্কাজনক'৷ (উত্তর শুনে টিচার রেগে গিয়ে) টিচার: তোরউত্তর হয় নাই৷আরও এক প্রকার জনক আছে৷ আমি তোরে এখন বেত দিয়া পিটাইমু৷আরসেইটা হবে তর জন্য 'বিপদজনক'৷  ছাত্র: স্যার আপনেরটাও হয় নাই৷আরও এক প্রকার জনক আছে৷ আমি এখন খিচ্চা দৌড় দিয়া পলামু৷ আর সেইটা হবে আমারজন্য 'সুবিধাজনক'৷  তখন পাশ থেকে আরেক ছাত্রউঠে বলল স্যার: আরেক প্রকার জনক আছে৷ আপনে যদি দৌড়াইয়া আবুইল্লারে না ধইরা আনতে পারেন, তবে সেইটা হবে আপনার জন্য 'লজ্জাজনক'৷ কি ব্রিলিয়ান্ট স্টুডেন্ট তাই না?  আর আপনারা এইপোষ্ট পইড়া যদি লাইক না করেন  এই পেইজে তবে সেথা হবে আমার জন্য 'অপমানজনক'. মজা পাইলে ঢিসুম-ঢিসুম কইরা লাইক মারেন তো দেখি।**** https://www.facebook.com/Tirtherkak.com.bd",0,celebrity
"you r great ,,sir",0,celebrity
"আমি সাদাসিধে মানুষ, এসব কমেন্ট টমেন্ট বুঝিনা... :/   বুঝলাম না এখানে একটা জ্ঞানগর্ভ পোস্টে এরকম কমেন্ট করে কেনো মানুষ?? 😞 কেউ বুঝিয়ে দিবেন??",0,celebrity
"উনাদের মাথা ব্যথা থাকবে কি করে নিজেরদের ছেলে-মেয়েদের তো পাঠিয়ে দেন বিদেশে,উচ্চ শিক্ষা গ্রহনের জন্য!অন্যের ছেলে-মেয়েদের ভবিষ্যৎ ধ্বংস হলেই কি আর না হলেই কি !তাই প্রশ্ন ফাঁসের দায় নিতে চান না!না চান এসবের পিছে দায়ীদের খুঁজতে! দিন শেষে ভিত্তিহীন,গুজব বলে উড়িয়ে দেন!",0,celebrity
এতের পোষ্ট পড়ে আমি গর্ববতি,0,celebrity
স্যারকে লিখতে দেখে ভীষণ শান্তি পেলাম।,0,celebrity
আমরা যখন আমাদের কোমলমতি শিশুদের অপরাধী  বানানোর নিয়ম অনুসরণ  করাই তারা ভবিষ্যৎ  এ আরো বড় অপরাধী হবে,0,celebrity
হাসি পায়,0,celebrity
কমেন্ট পড়ে শেষ ই করতে পারছি না 😬😬 😭😭,0,celebrity
আপনি আসল মানুষ। আপনারা লেখাটি না পড়েই অনেকে আছে বাজে মন্তব্য করে কে।,0,celebrity
অনেকেই দেখছি হৈ হোল্লা করছে যে প্রফেসর জাফর ইকবাল স্যার নাকি এই নিরাপদ সড়ক চাই নিয়ে চুপ। প্রফেসর জাফর ইকবাল স্যার যখন নিরাপদ সড়ক নিয়ে কাজ করেছেন তখন অামদের বর্তমার প্রজন্ম হয়ত অনেকেই অ অা শিখা হয় নাই। তার সড়ক নিয়ে ১ম কলাম বের হয় ১৯৯৯ সালে ভোরের কাগজে। অযথা হৈ হোল্লা না করে মন দিয়ে পড়ুন। জানতে পারবেন।,0,celebrity
তোমার কথা শুনলেই কেন জানি আমার বমি আসে,0,celebrity
১৯৭১এ একদল তরুন-যুবক তাড়া খাওয়ার পর সিংহের ন্যায় ঘুরে তাড়াকারিদের পালটা কামড় দিয়েছে। আরেকদল তাড়াখাওয়া কুত্তার মত পালিয়ে বেড়িয়েছে।  সেই তাড়াখাওয়া কুত্তাগুলা ইদানীং আমাদের মনের মাধুরী মেশানো লম্বা লম্বা বীরত্বের গপ্প শোনায়,0,celebrity
"#বঙ্গবন্ধু সার্বজনীন ? তাই যদি হয়, কেন এই দিনে কেক না কাটলেই নয় ?  কে #স্বাধীনতার #ঘোষক অজানাই থাকল ?",0,celebrity
জয় বাংলা,0,celebrity
"একদিন ঢাকা কলেজে আসুন না, স্যার।",0,celebrity
সালার পাঁচ টাকার সমুচা তেও কলিজা থাকে আজকাল! আপ্নের মত বুদ্ধিবেশ্যার তাও নেই....,0,celebrity
"আমি ও বিভ্রান্তি ছড়ালাম, প্রশ্ন ফাঁস হয়েছে।  অপেক্ষা করলাম কি শাস্তি পাওনা রইল। শালার গন্ডায় গন্ডায় পাশ করাটা দেশের উন্নতি হয় কেমনে। যার বই এর পাতা থেকে এখনো সুগন্ধ বের হয় সে পাশ করে কেমনে!!!",0,celebrity
"আপনি ছিলেন আমাদের সবার পার্থনায়,,এত সহজে আপনাকে যেতে দিব না,,,",0,celebrity
আল্লাহর কাছে দ্রুত এইমহান ব্যাক্তির জন্য সুস্থতা কামনা করছি।,0,celebrity
"স্যার, আপনি ভালো হয়ে ফিরে আসুন আমাদের মাঝে।আপনার মনের ক্ষত হয়তো আমরা পূরণ করতে পারবো না,তবুও সব  ব্যাথা ভুলে ফিরে আসুন।",0,celebrity
পুরা পাগলামিতে ভরপুর পোষ্ট। এই পোষ্টে হা হা রিয়েক্ট এত কম কেন? মেহিদী এমপির এরচেয়ে বেশি ছিল। চারের সম্মান রাখবা না নাকি তোমরা? কি যে করো?,0,celebrity
মি. জাফর দালাল,0,celebrity
"আপনি কি ১/১১ ঘটনা ভুলে গেলেন???? তখন আপনার এই পা চাটা লেখনী কোথায় ছিল???? আপনি আপনার জনপ্রিয়তাকে পুঁজি করে এমন দু চোখা বিচার বন্ধ করেন।৫ই জানুয়ারীর নির্বাচন কি ধরনের প্রহসন হয়েছিল তা দেশের সবাই জানে।তাই বলছি এই পা চাটা বন্ধ করেন। অন্যথায় যে জনগণ আপনাকে জনপ্রিয়তার তুঙ্গে নিয়ে গেছে,তারাই আবার আপনাকে জনপ্রিয়তার তলানিতে আনতে দ্বিধা বোধ করবে না। so be careful sir",0,celebrity
"ভাগগিস আপনার মা আর ভাই মরে গেসে, নাইলে আপনারে কি করতো ভাবতেসি",0,celebrity
আমার বাবার সৌভাগ্য তোমার মত ব্যাক্তি  সম্পর্কে জানতে পেরেছি 😆😆😆 তাই বলি তাড়াতাড়ি অক্কা খেয়ে ৪ দিন্না খাওয়ার সুযোগ করে দাও 😂😂,0,celebrity
রাস্তা ব্লকড থাকার জন্যে আপনার গায়েবানা জানা্যায় অংশ নিতে পারিনি। স্যার রাগ করবেন না। আমরা বুঝি মৃত্যূর পরেও ছাত্রদের নিয়ে আপনার চিন্তা কোনো অংশে কমেনি।তাই কবরে শুয়ে শুয়েই লিখছেন এত কিছু। আল্লাহ্‌ আপনাকে বেহেশত নসিব করুন।,0,celebrity
"ওনি অনেক আগে একটা বই লেখছিলেন,”ভুতের বাচ্চা সোলায়মান” আমিও বড় হইয়া একটা বই লেখব, “ফাকিং মাদারি জাফর”",0,celebrity
আপনি একজন পেইড দালাল সেটা সবার কাছে স্পষ্ট,0,celebrity
"কামিনি ফাইল,,,এক ফাইলে যথেষ্ট,,,লিঙ্গ বাঁকা কিংবা ছোট,নিস্তেজ হয়ে গেছে? আর নয় চিন্তা আর নয় ভাবনা,,,চেতনা তেল মালিশ করুন আর লিঙ্গ স্থায়ীভাবে মোটা করুন,,,চলে আসুন জাফর স্যারের কমেন্ট বক্সে দেখুন স্যারের ফাইল গুলো।😂",0,celebrity
একজন আয়েশা ফয়েজ না থাকলে আমরা একজন হুমায়ুন আহমেদ একজন জাফর ইকবালকে পেতাম না- ভাবলেও শিউরে উঠতে হয়। নতুন প্রজন্মকে বাংলাদেশের দিশা দেখালো যে মানুষেরা তাদের জন্মদাত্রীকে অবনত শিরে প্রণাম জানাই।,0,celebrity
আপনার বক্তব্যের সাথে মিল রেখে  আগামীকাল ছাত্রছাত্রীদের সাথে রাস্তায় নামুন। তাহলে আপনাকে দেখে হড় হড় করে বমি করবেনা!,0,celebrity
কমেন্ট কইরা লাভ নাই।জনাব কমেন্ট পড়েন না....,0,celebrity
যারে দেখতে নারি তার চলন বাঁকা আর যার দালালি করি তার পটি ও সুধা🐸,0,celebrity
সুযোগ সন্ধানী লোক জাফর ইকবাল।।যে কিনা আগে দেখে দর্শক তার লিখা টা খাবে কিনা।চেতনা ব্যবসায় জড়িত।,0,celebrity
"চোখের সামনে এই ভাবে মানুষের মৌলিক অধিকার ধ্বংস হতে দেখেও যারা দলীয় আনুগত্যের বাইরে এসে জাতির কাছে ক্ষমা চাইবেন না, এই জাতিও আপনাদের কোনোদিন ক্ষমা করবে না। লজ্জা বা ভয়ে হয়তো সামনা সামনি মুখে থুতু দিবে না, তবে মন থেকে ঘৃণা করবে আমরণ। আপনারা হলেন ২০১৮ এর রাজাকার।  নির্লজ্জ, নগ্ন বন্দুকের মুখে আপনাদের কিছু বলতে পারি বা না পারি, সামাজিক ভাবে বয়কটতো করতে পারবো, তাই না?  আপনাদের জন্য রইলো এক রাশ ঘৃণা। সেই সাথে দোয়া করি, আল্লাহ আপনাদের হেদায়েত দিন। সত্যকে সত্য আর মিথ্যাকে মিথ্যা বলার মত সৎ সাহস দিন। চক্ষুলজ্জা বাড়িয়ে দিন। আমিন।",0,celebrity
আমার হর হর করে বমি আসছিল কি জানি কি হলো,0,celebrity
বাহ দারুণ তো সবাই সবার বংশের পরিচয় দিয়ে কমেন্ট করছেন...  কমেন্ট গুলো আপনার বাবা/মা দেখলে খুবই প্রাইড ফিল করতেন...,0,celebrity
"আপনি কি বাংলা ভাষা,বাংলা বর্ণ ভালোবাসেন? তাহলে এখানে আপনার নাম ইংরেজিতে কেনো??",0,celebrity
স্যারের কোনো নতুন লেখা পাওয়া যাচ্ছে না কেন??,0,celebrity
"কে তুমি বৎস?ধরিয়া মৎস,বেচিয়া গন্জে অকুল ও কুন্জে,না খাইয়া তাজা কেন ভক্ষন করিয়াছো মেয়াদ উওীর্ণ গাজা 🐸🐸🐸🐸",0,celebrity
এতবড় লিখা হাইস্যকর :v,0,celebrity
"আপনি সেই বাপের সন্তান, যার মুক্তিযুদ্ধের বয়ান শুনে বঙ্গবীর কাদের সিদ্দিকী বলেছিলেন, "" আফসুস ! আজ রাজাকরের বাচ্ছার কাছ থেকে মুক্তিযুদ্ধের ইতিহাস শুনতে হচ্ছে!""",0,celebrity
আপনি এত রসিক কেন? নতুন বছরের শুরুতেও আপনার কৌতুক ভালো লেগেছে। হা হা দিলাম! Carry on..,0,celebrity
কবর থেকে পোস্ট আসে কিভাবে ???? 😮😮,0,celebrity
"সুস্থ্যতা কামনা করি,,,,,",0,celebrity
আমি তো ভেবেছিলাম আপনি মিম আর রাজিবের উপর হড়হড় করে বমি করে দিবেন।😱,0,celebrity
আমি এক মত স্যার। মেডিকেলের মত সকল পাবলিক বিশ্ববিদ্যালয়ের পরীক্ষা একটাই হোক।,0,celebrity
"আপনি লাইভ বুঝেন না?? তাহলে বুঝেনটা কি?? মাঝে মাঝে আপনার কথা শুনলে মনে চায়,আপনি যেই গর্তে থাকেন, ঠিক সেই গর্তের মুখটায় হরহর করে বমি করে দেই।",0,celebrity
কত ভন্ডামি আর করবেন ! আপনি এখন দুর্বল প্রকৃতির মানুষ বনিয়া গেলেন। অন্য সময় তো আপনাকে যুবক মনে হয়।,0,celebrity
অসংখ্য ধন্যবাদ।,0,celebrity
স্যার তুই এখনো মরিস নাই হায় আল্লাহ👿😂,0,celebrity
মদ খা। মদ না খাইলে তোরা মানুষ হবি না।,0,celebrity
কমেন্ট করার ভাষা হাড়িয়ে ফেলেছি। বাংলাদেশে এত্ত বুদ্ধিজীবী তা কমেন্ট না পড়লে বোঝতামই না। আমিই বোকা তাই স্যার এর পোষ্টে কিছু বল্লাম না.....,0,celebrity
"দালাল,চাটুকার",0,celebrity
""" বাইরে থেকে রফতানি করা এই গণতন্ত্রের কারণে শুধু ইরাকেই প্রায় পাঁচ লক্ষ মানুষ মারা গেছে "" একটি বিশেষ দলকে ডিফেন্ড করার জন্য জাফর সাহেব এখন গণতন্ত্র বিরোধী। মানুষ কতোটা দল কানা হলে এমন আচরন করে ।",0,celebrity
3কোটি নতুন চোর তৈরি হচ্ছে  :(,0,celebrity
"ছাগল পাগল, পাবনা গেলেও পাগলরা অারও পাগল হবে",0,celebrity
"দেশের নব্য শত্রু 'চাটুকার'.... রাজাকার হচ্ছে পরাজিত শত্রু।  রাজাকারে এখন ভয় হয়না, চাটুকারে হড় হড় করে বমি করে দি।",0,celebrity
"এত ফাপানীতি, রাজনীতি, পিছিয়েপড়া রাষ্ট্রনীতির বকবকানির মাঝে আপনার আশা ঝরা ভাষণ মন ভরালো।",0,celebrity
অামি রাজাকার,0,celebrity
Sir যারা collegeএ পড়ি তারা পারবো?,0,celebrity
আপনারা যা শুরু করছেন!! উনি এখন তসলিমার মত কমেন্ট করতে দিবে না। বন্ধ করে দিবে....,0,celebrity
আমরা আছি সাথে,0,celebrity
স্যার আমি আপনার পোষ্টের কমেন্ট পড়া ফ্যান.... এখন কমেন্ট গুলা পড়বো সময় পেলে কয়েক ঘন্টা পর আবার এসে পড়ার চেষ্টা করবো। হাসি-খুশী থাকলে শরীরের জন্য ভাল। (2),0,celebrity
ষ্যার ইজ ব্যাক,0,celebrity
একদম সত্য কথা লিখছেন স্যার।,0,celebrity
"একজন অন্তত আছেন, যিনি দেশ নিয়ে এবং তার সামাজিক দায়িত্ব নিয়ে ভাবেন।",0,celebrity
"অসাধারণ হয়েছে স্যার,,,,,",0,celebrity
এত কষ্ট নিয়ে বেচে থেকে কি লাভ? তারচেয়ে আপনি বরং সত্যি সত্যি মারা যান। একটা গুজব অন্তত সত্যি হয়ে ধরা দিক।  ওপারে ভাল থাকবেন স্যার।😂,0,celebrity
ষাঁড় জাফর ইকবালের পোষ্ট কেউ পড়ে না   তার পোষ্টে কমেন্ট বক্সের কমন পড়তে আসে,0,celebrity
গুজব,0,celebrity
শারার পুতে কি আগে পুরান জুতা চুরি করত নাকি!!,0,celebrity
আমার ও কথা গুলো শুনে গড গড করে বমি আসতেছে।আমাদের কে মুক্তিযুদ্ধের চতনা শিখাতে আসছে।এক জন নাস্তিকের কাছে মু্ক্তিযুদ্ধের গল্প শুনতে হবে এমনটি জানলে অনেক আগেই ফেসবুক থেকে ইস্তফা নিতে বাধ্য হতাম।,0,celebrity
স্যার এই পর্যন্ত যত কমেন্ট পড়েছে তা আমি পাঠ করার চেষ্টা করেছি। একটা মাত্র কমেন্ট আপনার পক্ষে। আমি অবাক হচ্ছি দেশে এতো  জামাত শিবির জন্মাইলো কেমনে? আপনি কমেন্ট গুলো প্লিজ পাঠ করুন।,0,celebrity
অসাধারণ! ! ধন্যবাদ স্যার!  সব ছেলেমেয়েদের একবার এই লিখাটা পড়া উচিৎ!,0,celebrity
"আপনার জন্য সারা দেশবাসীর শুভকামনা আছে স্যার, আপনি ভালো হয়ে উঠবেন, আবার  আপনার ক্যাম্পাস আপনার দৃপ্ত পদচারণায় মুখরিত হবে। আরো আরো মুগ্ধ নক্ষত্রগুলো বুভুক্ষুর মত পান করবে  আপনার কিশোর রচনাবলীর আস্বাদ। আপনাকে যে ভালো হতেই হবে। অবিশ্বাস্য সুন্দর পৃথিবীর রূপ রস গন্ধ স্পর্শ আরো আপনাকে আপ্লুত করবে। ভালো হয়ে উঠুন স্যার।",0,celebrity
"আপনার লেখা পুরোটা না পইড়াই রিয়্যাক্ট দিছি..😁 আর আমার রিয়্যাক্ট যে বৃথা যাবেনা,সেটাও জানি।",0,celebrity
"কলেজের ছাত্র-ছাত্রী রাজীব এবং মিম মারা যাওয়ার পর আপনার প্রতিক্রিয়াটি ও ছিল অত্যন্ত বিচিত্র! কিন্তু এই স্ট্যাটাস টা সপ্তমাশ্চার্যকেও হার মানাইসে! নো এপোলজিস, নো এক্সপ্লেনেশন যে আপনি আন্দোলনের এতদিন পর্যন্ত বা*র পাত্তাটাও দেননাই! আয়মান সাদিক কে আমরা মাফ করলে করতেও পারি, কজ সে *মাফ* চাইসে, অন্তত এইটুক ভদ্রতা দেখাইসে প্লাস ফিল্ডেও গেসে (মটিভ যাই হোক না কেন)। আপনে পাঁচটা মিনিট আপনার শহরের কোনো মিছিলেই মুখ টা দেখায়ে আসতেন? এতেই বাচ্চাগুলা কি পরিমাণ মটিভেশন পাইত! ঢাকায় তো আসার দরকার নাই! আচ্ছা ঠিকাসে এগুলা করার সাহস পান্নাই। অন্তত ""স্যরি"" দিয়ে তো শুরু বা শেষ করতে পারতেন লেখাটা, নাকি? উল্টা করলেন টা কি?                                                                                                     ""আমরা সবাই দীর্ঘদিন থেকে এই একই দাবি করে আসছি ""  এটা যে ছোট বাচ্চাগুলার রক্ত ঘামের ক্রেডিট চুরির একটা ডিক মুভ সেটা জানেন? আপনি নোভেল চুরি করলে কিছু যায় আসে না, বাট যেটা বাচ্চারা এতো কষ্ট করে অর্জন করসে সেটার জন্য আপনি যাস্ট কলাম লিখেই  বাহবা পাবেন টা ভাব্বেন না যেন।                                                                                           "" আমাদের সেই কথাগুলো কখনও কেউ গুরুত্ব দিয়ে শোনেনি""- কেম্নে শুনবে? কি করসিলেন? কিভাবে চেষ্টা করসিলেন? ঐযে একাত্তরের সময় যেভাবে দেশকে স্বাধীনের চেষ্টা করসিলেন সেভাবে? আপনি বাদই দেন। আপনার সাহিত্য আর মজা লাগে না। ওইসময়ও আপনে স্ট্র্যাটেজী করতে করতেই দেশের আসল ব্যাটা ছাওয়ালরা দেশ নিরাপদ করে ফেলসিল! আর তাঁদের যোগ্য উত্তরসূরীরা এবার সড়ক নিরাপদ করবে। এরপর সেটা নিয়ে আমরা আমাদের বাচ্চাদের গল্প শোনাব, বই লিখব, কীভাবে তাদের সুন্দর ও নিরাপদ ভবিষ্যৎ এর জন্য একদল পাগল ছেলেমেয়েরা নতুন করে যুদ্ধ করে মুক্তিযোদ্ধাদের মুখ রাখসিল! কীভাবে আর একদল সেইযুদ্ধে বুইড়া আঙ্গুল দেখায়ে ভাঙতে চাইসিল। এবং পরে সাবধানও করে দিব যে কীভাবে ওই বুইড়া আঙ্গুলরে ""গুডলাক""এ কনভার্ট করে সেইদল এখন ক্রেডিট চুরি করে বেড়াচ্ছে। সবশেষে দশ নম্বরের ক্রিটিকাল থিংকিং কোয়েসশশান থাকবে- ক) নিরাপদ সড়ক যুদ্ধের প্রথম শহীদদের নাম লিখ।-১ খ) ছাত্রদের যানবাহনের লাইসেন্স চেক করার কারণ অল্প কথায় লিখ।-২ গ) জাতির জনকের বাংলাদেশ এবং ছাত্রদের নিরাপদ বাংলাদেশ স্বপ্নের মধ্যে সাদৃশ্য দেখাও।-৩ ঘ) ""বুইড়া আঙ্গুল দেখানোদের ক্রেডিট চুরি এবং মুক্তিযুদ্ধ পরবর্তী সময়ে একদল মানুষের মুক্তিযোদ্ধা সার্টিফিকেট চুরি আসলে একি""-উক্তিটির যথার্থতা যাচাই কর।-৪ *****বোনাস প্রশ্নঃ তুমি কি মনে কর কোটা আন্দোলন এবং নিরাপদ সড়ক আন্দোলন এক সুতোয় গাঁথা?-A+*****",0,celebrity
যানা মতে এই পোস্টের কোন কমেন্ট জাফর সাহেব পড়বেনা কোন দিনই না,0,celebrity
"এই প্রথম আপনার কোনো স্ট্যাটাসের সাথে একমত পোষণ করছি।কোচিং বাণিজ্যের সাথে মুক্তিযুদ্ধের চেতনা জুড়ে দেননি দেখেই ভালো লাগছে।যাক,দেরিতে হলেও বুঝেছেন যে সবকিছুতে মুক্তিযুদ্ধের চেতনা জুড়ে দেওয়া ঠিক না।😁😁",0,celebrity
সাজ্জাদ হোসাইন কমেন্ট গুলা বেশি জোশ.. ধন্যবাদ বন্ধু..  হালকা বিনুদুন নেওয়ার সুযোগ করে দেওয়ার জন্য...,0,celebrity
"মাছের পচন শুরু হয় মাথা দিয়ে, গাছের পচন শুরু হয় পাতা দিয়ে আর মানুষের পচন শুরু হয় বিবেক দিয়ে। আপনি পচে গেছেন স্যার।",0,celebrity
"Sir, আমার ছেলে এবার PECE দিবে। I think it is also a torture for class five's students.",0,celebrity
সাতসকালে আপনার খবর দেখে হাসতে হাসতে হিসু করে দিয়েছিলাম। এরপর এই লেখা/পোস্ট পড়ে হাসতে হাসতে হাগু করে দিলাম। এখন হয়ত হড়হড় করে বমি করে দিবো। কেমনে পারেন... http://www.ittefaq.com.bd/capital/2018/08/31/169028.html,0,celebrity
আল্লাপাক রাব্বুল আল আমীনের কাছে আপনার সহজ সহসা সুস্থতা কামনা করছি।,0,celebrity
wish u a very happy birthday sir,0,celebrity
স্যার বাংলাদেশে নাকি দালাল চাষ হচ্ছে কোন এক টিবিতে দেখলাম তাও এবার বাম্পার ফলন বৃষ্টি ছাড়াই।,0,celebrity
দুধের মাঁছি।,0,celebrity
আরেকটি জয় বাংলা পরিবেশনা।,0,celebrity
"যে মানুষ তার স্ট্যাটাসে খোদার নামটা অন্তত স্বরণ করেছেন তাকে কিভাবে পুরাপুরি নাস্তিক হিসাবে টাইটেল  দেওয়া যায়? তার কয়েকটা বই পড়ে মাত্র? বই তো লেখেন কারণ তার সেই যোগ্যতাটা আছে ঐ রকম লেভেলে আর্গুমেন্ট করার। আর মতপার্থক্য তো সেখানে থাকবেই। একটা জিনিস খালি জানতে চাই উনি কি কোন দিন তার শিক্ষকতার জীবনে ক্লাসের ছেলে-মেয়েদের বলছেন যে তোমরা আল্লাহ্‌কে বিশ্বাস করো না, এসব ভুয়া বেপার সেপার? যদি তা না হয়ে থাকে সে নাস্তিক হলেও সীমালঙ্ঘনকারী না। আমি নাস্তিকতাকে প্রশ্রয় দিচ্ছি না কিন্তু দেশের একজন সুশিক্ষিত মানুষের উপর আঘাতটা করা হয়েছে সম্পূর্ণ ভিন্ন উদ্দেশ্য হাসিলের জন্য। আর সেখানে ধর্ম আর সংস্কৃতিকে এক করে হলি খেলা হচ্ছে। যাতে পাবলিক কালারড হয়ে যায় আর সেই রঙ ধোয়ার জন্য কেউ পানি নিয়ে আসে। সুস্থ হউন তাড়াতাড়ি জাফর ইকবাল। আপনি একজন বুদ্ধিমান মানুষ আপনাকে যেমন অনেক সম্মান করি তেমন আমার নিজের মতপার্থক্যকেও ঠিক ততটা গুরত্ব দেই। :)",0,celebrity
ভাবতে লজ্জা লাগে যে একসময় আপনার ভক্ত ছিলাম।,0,celebrity
"আপ্নারা কেউ এই স্টাটাস দেখে বিভ্রান্ত হবেন না, স্যার বেছে নেই, এটা তার এডমিন এর লিখা স্যার এর লেখা হলে হড় হড় করে বমি হতো। আগামীকাল জুমার নামাজ এর পর জাফর স্যার গায়েবি জানাজা হবে, যে যে স্থানে থাকবেন জামাতে আকারে পড়ে নিবেন।",0,celebrity
পোস্ট না পড়লেও আপনার পোস্টের কমেন্ট মিস করতে চাই না। হাজিরা দিয়া গেলাম 😑,0,celebrity
আহত কোন কলেজ ছাত্রকে পানিতে ফেলে দেয়ার ঘটনা ঘটেছে নাকি বিশ্ববিদ্যালয়ের কোন ছাত্রকে? আমি যতদূর পড়েছিলাম ছেলেটি নর্থ-সাউথ বিশ্ববিদ্যালয়ের ছাত্র ছিলো। আপনি কি বিষয়টা ভালোমতো না জেনেই কন্টেন্ট বানিয়ে দিলেন?,0,celebrity
"আমাদের দেশে বর্তমানে নাগরিক ঐক্য খুবই দরকার। যখন এই নাগরিক ঐক্য হবে তখন এই নিরিহ নাগরিকদের জিম্মি করে রাজনিতি করার দুসাহস কেউ দেখাবে না। আমাদের দেশের ৯৫% মানুষ পেটনীতি করে, কিন্তু এই সংখ্যালঘু রাজনিতিবিদের কাছে আমরা জিম্মি। তাহলে গনতন্ত্র কোথায়?",0,celebrity
"একটা দলের হয়ে দালালি এখনো ছাড়লেন না,কমেন্টগুলা পড়েন,দেখেন কত মানুষ আপনার উপর বমি করতেছে",0,celebrity
কমান্ট করতে এলুম মাগার ভাই-ব্রাদাররা যা দিছে😂😂😂😂,0,celebrity
শ্রদ্ধেয় ষাঁড় যদি কমেন্টগুলো পড়তেন তবে নিশ্চিত প্রেগনেন্ট হয়ে যেতেন! :p,0,celebrity
এখানে দেখছি অনেকে স্যারকে খাটো করে কথা বলেছেন।তাঁর মতের সাথে আপনার মত নাও মিলতে পারে।কিন্তু জাফর  ইকবাল নামটার জন্য হলেও তো ন্যূনতম শ্রদ্ধা তিনি পাওয়ার যোগ্য।,0,celebrity
পড়ে খুব ভালো স্যার! ধন্যবাদ,0,celebrity
মোহাম্মদ শাহ্জাহান আপনার বক্তব্য এখানে পেশ করেন,0,celebrity
রুহুল আমিন গৃহবধূটিকে ধর্ষণ না করে আপনাকে ধর্ষণ করলে এতক্ষণে তার ফাসি হয়ে যেতো।,0,celebrity
"ঐ সময়েও বুদ্ধিজীবীরা আক্রান্ত হয়েছিল,এই সময়েও আক্রান্ত হচ্ছে নির্বিচারে!সময়ে সময়ে কোন পার্থক্য নাই।শুধু লোকগুলো বদলেছে.....!!",0,celebrity
"কে চায় জামায়াত ইসলামী নির্বাচনে অংশ নেয়ার সুযোগ পাক? আমি চাই না, এই দেশের কারো সেটা চাওয়া উচিত না। কারণ হিসেবে আপনার লেখা থেকেই বলছি, ""যারা চায়নি বাংলাদেশের জন্ম হোক, এই দেশের মাটিতে তাদের রাজনীতির অধিকার তাদের নেই।""কিন্তু আপনার প্রতিও আমরা বিরক্ত স্যার। মুক্তিযুদ্ধে মুক্তিযোদ্ধারা যূদ্ধে গিয়েছিলাম পিপলস পালস অনুভব করে, সময়ের প্রয়োজনে। কোটা আন্দোলন,নিরাপদ সড়ক চাই আন্দোলন হয়েছে সময়ের প্রয়োজনে। যেটা আপনি অনুভব করার যোগ্যতা রাখেন না।",0,celebrity
"জিয়াকে নিয়ে মিথ্যাচার। মুক্তিযুদ্ধের চেতনার নাম করে যখন হাসিনা ভোট চুরি করে তখন আপনার খারাপ লাগেনা, জয় বাংলা বলে যখন ছাত্রলীগ ধর্ষণ করে তখন খারাপ লাগে না??",0,celebrity
"স্যার, অত অতীতও হয়নি এখনো। গত বছর শুধুমাত্র পত্রিকার নিউজের ভিত্তিতে গণধর্ষণ করা হয়েছে ১৮২ জন নারীকে। গত পাঁচ বছরে এই সংখ্যা ১০০৮ জন! কিন্তু আপনি জানবেন কী করে, আপনি তো ঘুমে থাকেন! গর্তে থাকেন! মুখে বমি নিয়ে বসে থাকেন!!",0,celebrity
আপনি কুত্তার মত দালালি করেন,0,celebrity
"স্যার একটু চুলটানা কামালের লাইগা দেহা করতে গেছিল,তাই সময় পায়নাই।",0,celebrity
হা হা রিএক্ট কেম্নে জানি দেয়? ভুইলা গেছি!,0,celebrity
ওরে কমেন্ট :D :D,0,celebrity
আগে কি ঘুমাইতেছিলেন? সব প্রশ্ন ফাশ হয়ে যাওয়ার পড় ঘুম ভাঙ্গছে??,0,celebrity
yes,0,celebrity
"হাইস্যকর,ব্যাপারটা হাইস্যকর।",0,celebrity
"আমরা মৃত্যুর দরজা থেকে ঘুরে না আসা পর্যন্ত বুঝিনা যে এই পৃথিবীতে আমাদের জন্য কত অজস্র মানুষের ভালোবাসা লুকিয়ে আছে। জাফর স্যার, আপনার সায়েন্স ফিকশন সবগুলো পড়া না হলেও সবগুলো কিশোর উপন্যাস পড়া হয়ে গেছে। আপনার সৃষ্টি করা ডাব্বু, লাবু, হাতকাটা রবিন, দীপু, রাশেদ চরিত্র গুলো আমার কল্পনা জগতের হিরো। ছোটবেলা থেকেই ইচ্ছা শাহজালাল ইউনিভার্সিটি তে ইঞ্জিনিয়ারিং পড়বো। এবার এইচএসসির পর যদি স্বপ্নটা পূর্ণ হয় তাহলে আপনার সাথে  একবার হলেও দেখা করতে চাই স্যার। আপনাকে কেউ মারতে পারবেনা। দেশের ১৬ কোটি মানুষ আপনার সাথে আছে। আর আপনি বাঙালির অন্তরে বেঁচে থাকবেন অনন্তকাল 💜💜💜",0,celebrity
আমি এখন মদ খাব আর কমেন্ট পড়বো।🐸,0,celebrity
"এই লোক হচ্ছে চরম পর্যায়ের ইতর। পোস্ট দিয়ে সে গর্তে লুকিয়ে যাবে, কমেন্ট পড়বে না। আর মাঝে মাঝে বলবে আমি ফেসবুক লাইভ কি জিনিস বুঝি না। এই লোক ধর্মান্ধতার বিরুদ্ধে কথা বলে কিন্তু সে নিজেই তার আইডিওলজির ব্যাপারে উগ্রভাবে অন্ধ। যে কাউন্টার মন্তব্য, আর্গুমেন্ট শুনতে রাখি নয় তার কথার দু পয়সার দাম নেই। সে নিজে যা বিশ্বাস করে বলে যাবে কিন্তু আরেকজনেরটা শুনবে না, নিবে না। জাতি নিজের চিন্তায় উগ্র অন্ধ বিশ্বাসীকে যত দ্রুতই চিনবে ততই কল্যাণকর!",0,celebrity
আমাদের এগিয়ে যাবার পথে বাধা এই ধরনের তথা কথিত বুদ্ধিজীবী!,0,celebrity
"""আমি সেই রাজনীতি চোখ দিয়ে দেখব; কিন্তু মন থেকে বিশ্বাস করতে হবে কে বলেছে?""",0,celebrity
"কাকারে কমেন্ট কইরা লাভ নাই কাকায় রিপ্লাই দেয় না, কানা কাকায়।",0,celebrity
দারুন একটা লেখা,0,celebrity
"আজ বাংলাদেশ জিতলে ""আমার দেশ"" লিখে একটা পোস্ট কইরেন।",0,celebrity
স্যারকে এখন কিছু উত্তর করতে পারছি না । 😨,0,celebrity
"স্যার এরা বাঙালি বলে কথা ৤তাই তু তাদের স্থান আজ বিশ্বে হলনা৤আর যারা আপনার লেখা পড়ে বুমি বুমি ভাব দেখায় তার কি জানেন স্যার ?আপনি ত বিজ্ঞানে ছাত্র তাই অবস্যই জানবেন তবু আমি বলি ,তারা হয়তু পচা নর্দমা থেকে যাতা খেয়ে অসুস্থ হয়ে পড়েছে অন্যতাই তারা সবাই প্রেকনেট ,,৤স্যার আপনি আবস্যই জানেন  ""সমাজে ন্যায় প্রতিষ্টা করতে চাইলে কিছু মৌলবাদি তো খানা দিবেই""যারা চেচামেচি করতেছে তাদের ৫ জনেও ছিনেনা ৤কিন্তু আপনাকে তু অনেকে চিনে তা কমেন্ট আর লাইক দেখে বুঝা যায়৤ কথায় আছেনা স্যার "" খালি কলসি বাজে বেশী!""",0,celebrity
সবার এত ভালোবাসা দেখে আপনি হড় হড় করে বমি করে দিবেন না প্লিজ :-),0,celebrity
স্যার এতদিন কোথাই ছিলেন?,0,celebrity
আজকে তো স্যারের গায়েবানা জানাযা !,0,celebrity
"স্যার এ দেশে আমার্না, এ দেশ আপনার না, এ দেশ মৌলবাদীদের, এ দেশে আর থাকতে মন চাইনা, আমরা আপনার নিরাপত্তারর জন্য এটাই কামনা করি জাদুঘরে আপনাকে আয়নার গ্লাসে নিরাপত্তার সহিত বন্দি করে রাখা হোক,ওখানেই নিরাপদ,  ওখান থেকে বসে #তোমরা_যারা  কলাম লিখবেন।",0,celebrity
"জাফর ইকবাল স্যার শহীদুলের জন্য মায়াকান্না করছেন। কথা হলো, বাংলাদেশের ইতিহাসে সবচেয়ে বড় উন্নয়ন এখন হচ্ছে। তালিকা দিতে গেলে ফুরাবে না। এক চোখ কানারা অবশ্য সরকারের কিছু অসফলতার তালিকা নিয়ে দৌড়াদৌড়ি করেন। আন্তর্জাতিক মিডিয়ার সামনে যদি সরকারের সফলতা নিয়ে শহীদুল সাহেব আগে কখনো কথা বলে থাকেন, তবে এবারের টাকে ""অগঠনমূলক সমালোচনা""র মর্যাদা দেয়া যাবে। আর যদি না বলে থাকেন তবে একে 'ষড়যন্ত্র' বলা যাবেনা ?! আর মাত্র দশ বছর। এরপর দেশ মালয়েশিয়ার চেয়ে কম হবেনা। আপনারা বুড়া ধাড়ী গুলা এত বছর শুধু রাজনৈতিক স্বার্থে আন্তর্জাতিক ভাবে দেশের ইজ্জত মেরে,এখন নতুন বৈশ্বিক প্রজন্মের স্মার্টনেস দেখে, ধরা খাওয়ার ভয়ে এসেছেন পিঠ চাপড়াতে। আপনারা চালবাজি ধরিবাজি ছাড়া কি শিখিয়েছেন এতদিন ? এরা ইন্টারনেট স্বশিক্ষিত পোলাপান। ইন্টারনেট ও বিদ্যুৎ সংযোগ এখনকার মতো নিরবিচ্ছিন্ন থাকলে এরাই দেশ বদলে দেবে। সুশীলেরা দূরে গিয়া মরেন। আর গন্ধ ছড়ায়েন না।",0,celebrity
"এই অপকর্ম এর দায় আপনার, আমার। যদিও আমরা না বোঝার ভান করছি।",0,celebrity
" প্র:কোনটি সত্য?  উ:গরমের দিনে কুত্তা জিহ্বা বের করে দৌড়ায়।   গরমের দিনে কুকুর জিহ্বা বের করে দৌড়ায়, ঠিক! বইয়ে লেখা আছে তাও ঠিক। তাই বলে এ ধরনের আজগুবি(আসলে বাস্তব) প্রশ্ন পরীক্ষায় দিলে দুইজন কি দুই'শ জন পাশ করবে জানিনা, তবে আমার নিজের কথা বললে আমি দুইশতবারেও একবারও পাশ করতে পারবনা। কে কী রকম করে জানিনা, তবে পৃষ্ঠা নম্বর মুখস্থ করার কোন শিক্ষা এযাবৎকালে আমি পাইনি, কৌশলটা কী রকম তাই বলতেও পারবনা।  উচ্চমাধ্যমিকের পড়ালেখা গতবছর থেকে সংক্ষিপ্ত করা হয়েছে, সেখানে কি কুত্তা দৌড়ানো পড়ালেখা বাদ দেওয়া হয়েছে, নাকি ওগুলোই রেখে বাকি সব বাদ দেওয়া হয়েছে তা উপরের লোকজন জানেন, তাদের খোদা জানেন, আমি জানিনা।",0,celebrity
"আমি মনে করি,,, বিশ্ববিদ্যালয়গুলোর নিয়ম,,সারা দেশের ",0,celebrity
ষাঁড়ে হাম্বা হাম্বা করে,0,celebrity
ꠀꠝꠣꠞ ꠜꠣꠡꠣ ꠀꠝꠣꠞ ꠉꠞꠛꠅ✌ আমার ভাসা আমার গরবও ✌,0,celebrity
"আমি কিছু গুরুত্বপূর্ণ কথা বলতে চাই।  ১.এখন বুঝতেছি কেন আপনার গায়েবা জানাযায় ২৫ হাজার(কম বেশি হতে পারে)মানুষ গোয়িং দিয়েছিলো।।আমার মতে এটা একটা বিশ্বরেকর্ড আর গিনেজ বুক অব ওয়াল্ড কে এটা জানানো দরকার।  ২.বলিউডে কিং অব কমেডি কপিল শর্মা ঢালিউডের কিং অব কমেডি জাফ্রু স্যার,। উনার উনার কমেন্ট বাকসো দেখলেই বোঝা যায়।।।  ৩.উনি কিন্ত অনেক বড় বিজ্ঞানী,তাই একটু উলটা পাল্টা বলে ফেলে এটা নিয়ে রাজনীতি করার দরকার নেই৷    আরেকটা কথা উনার জানায় পৃথিবীর রেকর্ডসংখ্যক মানুষ আসবে স্ক্রীনশট নিয়ে রাখেন।৷   ৪.আপনার কি মন খারাপ,আপনি কি ডিপ্রেসড, দুঃচিন্তা আপনাকে আকডে ধরেছে তাইলে আর নই চিন্তা নিয়ে এসেছি আমরা জ্রাফু স্যার কে, উনার পেইজে যান উনার লিখার নিচে ডুকে কমেন্ট পড়ুন।।আপনার কন ভালো হতে বাধ্য,এক লেখায় যথেষ্ট। কোন পার্শ্বপ্রতিক্রিয়া নেই।।।।  ধন ন্য বাদ।।।ভালো থাকবেন জাফ্রু স্যার।  অ হা আমি কিন্তু কমেন্ট পড়তে এসেছিলাম",0,celebrity
বি সি এস দিতে পারবেন আশা করি,0,celebrity
গর্ত থেকে আর এক দালাল বেড়াইতে আয়ছে!! আসেন আসেন একটি মোটিভেশন দিয়ে যান । ঔ শুনছিলাম আপনার নাকি বুমি বুমি বাপ এখন তাহলে তারসাথে মাথা ঘুরায় নাকি? এটা কিসের লক্ষণ! কয় মাস বাকি আছে আপনার এই অকাম টা কে করছে বুঝি টাক্কু নাকি??,0,celebrity
আমরা দেশ নিয়ে এত হতাশ। কিন্তু এই লোকটা যে এই দেশ নিয়া কত পজেটিভ চিন্তা করে!!! আমি শিওর উনি আমেরিকা থাকলে ভবিষ্যতে মার্কিন প্রেসিডেন্ট হইতেন।,0,celebrity
আমি কমেন্টস পড়তে আসছিলাম :-) :-),0,celebrity
আমার না বলা কিছু ভাষা ছিল ।বোঝার একটু সময় হবে ?,0,celebrity
ভূত আসছে 😎😎😎😎,0,celebrity
"সৃজনশীল শিক্ষা ব্যবস্থা তো আপনার পরামর্শের চালু হইছে। একবার ও ভাবেন নাই শিক্ষকরা এটার উপযুক্ত ছিল কি না।  আপনারাই ছাত্রছাত্রীদের প্রাইভেট, কোচিং করতে বাধ্য করেছেন।",0,celebrity
কোথাকার পায়জামা কোথায় নিয়া লাগাইলেন? কিসুই বুঝলাম না।। bd এয়ারপোর্ট থেকে গেলেন NY তারপর গেলেন ট্রাম্পের কাসে মাঝখানে আবার জামাত শিবিরো আইলো। কি কইতে চান direct বলেন না ষার। পিলিজ।☹☹☹,0,celebrity
সত্য সবসময় তিতা হয়।এত মানুষ বিরোধী করলো কিন্তু কেউ এইটা বলার সাহস করেনা যে আন্দোলন এ আসলেই মুক্তিযোদ্ধাদের অসম্যান করা হইছে যা কোনভাবেইই উচিৎ হয় নাই।মুক্তিযোদ্ধা দের অপমান কইরা লাভ কি হইছে?আন্দোলন বিতর্কিত হওয়া ছাড়া কিছু হইছে বইলা দেখি না।শুরুতে অরাজনৈতিক সকলের সাপোর্ট ছিল এখন তা প্রশ্নবিদ্ধ হইছে।হায়রে মেধা/জ্ঞান আমাদের!ভুল স্বীকার করতে রাজি হবে না।,0,celebrity
"কথাগুলো তিনি খুব সাবধানতার সাথে বলেছেন! কিছু কিছু জায়গায় ফাঁক রেখেছেন, যেনো ধরি মাছ না ছুঁই পানি!",0,celebrity
একটা সময় ছিল কত মানুষ ওনাকে শ্রদ্ধার চোঁখে দেখত অতছ আজ ওনি নিন্দার পাত্রে পরিনত হল । যে ছাত্ররা উনাকে দেখে সম্মান করত করতালি দিত সেই ছাত্র রা আজ নাকি উনার উপর বমি করে থুথু দেয় । উনাকে যখন কোপানো হল ছাত্ররা প্রথম রাস্তায় নামল । উনি আজ জনপ্রিয় লেখক হয়ে ছেন ছাত্রদেল জন্যে । উনি এইরকম না করলে পারতো ছাত্ররা উনার কাছ থেকে উচিত কথা আশা করেছিল যারা উনার জন্যে রাস্তায় নামল মিছিল করলো জুড়ালো আন্দলন গড়ে তুলল । ছাত্রদের ন্যায অধিকার আদায়ে ওনাকে পাশে চেয়েছিল এইটা বেশি কিছু না ।। বঙ্গবন্ধু যদি ন্যায কথা না বলত দেশ আজ স্বাধীন হত না ।। জাফর ইকবাল অচিরেই হারিয়ে সমাজ থেকে । আগামীর বই মেলা হবে তার বড় প্রমাণ ।,0,celebrity
"স্যার আপনার ভাইয়ের লিখাটা পড়ে জানতে পারলাম আপনি মুক্তিযুদ্ধকালে ১৯ বছরের যোবক থাকা সত্বেও যুদ্ধে যান নাই। তার মানে আপনি ভীরু ছিলেন, আপনার মাঝে বিন্দু পরিমান দেশপ্রেম ছিলো না। থাকলে অন্তত দেশ ও দেশ মাতৃকার সেই অসময়ে আপনার মতো যোবক গর্তের ভিতর নিজেকে লুকিয়ে রাখতেন না। আপনার ভাই তার লিখায় প্রকাশ করেছেন যে, আপনি সত্যি সত্যি গর্তে লুকিয়ে ছিলেন।  আর সেই আপনি এখন মানুষকে মুক্তিযদ্ধের গল্প শুনান। বিষয়টা খুব হাস্যকর। মুক্তিযোদ্ধারা যদি জানতেন '৭১ এর সেই ভীরু, কাপুরুষ, গর্তের জাফর এখন মানুষের মাঝে মুক্তিযুদ্ধ নিয়ে কথা বলে আর নিজেকে সাচ্চা দেশপ্রেমিক হিসেবে উপস্থাপন করে তাহলে নিশ্চয় তারাও গলায় আংগুল ঢুকিয়ে আপনার মুখের উপর হর হর করে বমি করে দিতো। লজ্জা হয় আপনাদের মতো সুশীল দের জন্য। ধিক্কার জানাই আপনাদের সুশীলতার।",0,celebrity
দোস্তো...😁😃😂 HA BE EB,0,celebrity
বমিবাজ জাফর সাহেব কি অবস্থা? গর্তে আর কতদিন থাকবেন? ভাল্লুকও গর্ত থেকে বের হয়ে আসে। শিক্ষকতা ছেড়ে দিন। আপনাকে সম্মান করলে শিক্ষকদের অপমান করা হয়।,0,celebrity
"অসাধারণ লেখা স্যার! আপনার প্রশ্নের দুপক্ষই দোষী। তবে দ্বিতীয় পক্ষকে অধিকতর দোষী হিসেবে মনে করি। কেননা এরা একটি জাতির আত্মপরিচয় মুছে দিতে চেষ্টা করেছিল। কঙ্গোর প্যাট্রিস লুমুম্বা, চিলির সালভাদর আলেন্দে, ব্রাজিলের জোয়াও গোলার্ট, ইরানের মোহাম্মদ মোসাদ্দেক, গুয়াতেমালার জ্যাকাবো আরবেঞ্জ,  ঘানার কোয়ামে নত্রুমা এই নামগূলোর সাথে আরো দুটো নাম যোগ করতে চাই। পানামার ওমর তেরিহোস (১৯৮১) এবং গ্রানাডার মরিস বিশপ (১৯৮৩)। এই দুজনও পশ্চিমা ষড়যন্ত্রে নিহত হন।",0,celebrity
কেউ হয় হুমায়ুন আহমেদ আর কেউবা জাফর ইকবাল।,0,celebrity
"স্যার, গর্ত নিয়ে গল্পের বইটা কি এবছরই প্রকাশ পাচ্ছে?",0,celebrity
"ছোটবেলায় আপনার লেখা পড়তাম। খুব সম্নানের চোখে দেখতাম আপনাকে। আজকের লেখাটা পড়ে স্তব্ধ হয়ে গেলাম। এমন একপেশে লেখা কীভাবে লিখলেন? আপনার কাছে কয়েকটি প্রশ্ন আমার- ১।আমরা মুক্তিযোদ্ধাদের অসম্মান করছি,নাকি বৈষম্যমূলক কোটা ব্যবস্থার সংস্কার চাইছি? ২। আমরা কি কোটা বাতিলের আন্দোলন করছি? ৩। ভিসির বাসা কি সত্যিই গুঁড়া গুঁড়া করে  ফেলা হয়েছে?  রাজাকার শব্দটাকে এখন আপনারা বৈষম্যের শিকার মানুষদের দমিয়ে রাখার অস্ত্র হিসেবে ব্যবহার করেন। শব্দটার মধ্যে যে নেগেটিভ অর্থ পুঞ্জিভূত ছিল, লীগের মেরুদণ্ডহীন পা-চাটা গোলামদের জন্যই তা আজ হারাতে বসেছে!",0,celebrity
চাকুরির পরীক্ষার জন্য কিছু একটা করেন... এটা আরো কষ্টের...!!! সকল সরকারি চাকুরির পরীক্ষা নিজ নিজ জেলায় নেওয়া হোক। কিছু বলেন স্যার।,0,celebrity
যে সবসময় মিথ্যা বলে তার আর সত্য বলার সৎ সাহস থাকে না৷ বিদেশী জার্নালিস্টকে সাক্ষাৎকার দিতে শহীদুল আলমের মতো সৎ সাহস থাকতে হবে৷ জাফর ইকবালের মতো লোক তো মিথ্যা পক্ষে সাফাই গাইতে আর মিথ্যা ছড়ানোর জন্যেই জন্মায়৷ নর্দমার কীট নয় বরং নর্দমা৷,0,celebrity
"আপনি পোষ্ট দিলেই আমার অনেক খুশি খুশি লাগে তবে আপনার স্ট্যাটাস পড়ার লোভে নয় বরং কমেন্ট পড়ার লোভে!  আপনি ট্রেঞ্এ কম্বল নিয়ে যেতে ভুলবেন নাহ , কারণ বাচ্চা পোলাপান আপনি ট্রেঞ্চে আছেন জানলে সুসুসু করে হিসি করে দিবে আপনার গালে!",0,celebrity
কমেন্ট গুলো পড়লেই বিনোদোন,0,celebrity
"আমি আপনার লিখাটিতে লাইক দিলাম, কারন আপনি শেষে আল্লাহর নামটি উচ্চারন করেছেন। আমি আপনাকে আহ্বান করছি,অনুরোধ করে বলছি আপনি আল্লাহর প্রতি পূর্ণ বিশ্বাস স্থাপন করুন, আল্লাহর রসুল(সাঃ) কে ভালোবাসুন সম্মান করুন, সারা দুনিয়া আপনাকে শ্রদ্ধা করবে। প্লিজ আর একটি বারও আল্লাহ, তার রসুল(সাঃ) এবং তার কোরআনকে অবমাননাকর কোন কথা বলবেন না।",0,celebrity
সবাই স্যারকে খেলে দিচ্ছে....,0,celebrity
"কিছু কিছু রাজাকারের সন্তানেরা,,,,, তোমরা বুদ্ধিমান বটে কিন্তু তোমাদের কথা বলার ল্যাংগুয়েজ এখনো অতিনিম্নমানের।।। স্বঘোষিত মেধাবী হয়েছ বটে কিন্তু মানুষ হতে পারনি।।। রাজাকার প্রজন্ম বলে কথা। মুক্তিযুদ্ধের কথা বললে গা  জ্বালা করে সেই সাথে চুলকানিটাও বেড়ে যায়।।।",0,celebrity
জাফর ইকবালের মত চেতনাবাজদের আগেও ঘৃণা করতাম এখনো করি। আগামী প্রজন্মের মধ্যে #জাফর_ইকবাল নামে যেনো কেউ না হয়।  এটি একটি আধুনিক ভাইরাসের নাম😁😁😁😁,0,celebrity
আল্লাহ আপনি জীবিত 😱😱,0,celebrity
"স্যাটেলাইট কাজ দিচ্ছে, পাগলের চিকিৎসা হবে খুব শিগগির!  এখন শুধু একবার লা হাওলা ওয়ালা কুয়্যাতা ইল্লাহ বিল্লাহ পড়ে যাও!   তারউপরে এর লেখা প্রবন্ধ নাকি,আমাদের পড়ানো হবে, আল্লাহ হেফাজত করুক! :3  Mukitul Hoque",0,celebrity
"এটা কেমন কথা আমি বিডিও দেখিনাই।লাইভ কি বুঝিনা।তাহলে সাপাই গাইতে আইলেন কেন? সত্য কথা হল সত্য বলতে ভয় পাই যদি আপনা দের,,,,,,,, নষ্ট  হয়ে যাবে।",0,celebrity
দোষটা কার ঘাড়ে দিলেন? আগে সেটা পরিষ্কার করলে ভালো হতো না?,0,celebrity
"ভাইস চ্যান্সেলর হতে না পারার চাপা কষ্ট ঝরে পড়ছে। চাকুরীর মেয়াদ প্রায় শেষ, এখনো ব্যাপারটা আমলে নিচ্ছেনা সরকার! এত চাটামির মূল্য এই??",0,celebrity
"আমরা পাড়াগাঁয়ে থাকি তবুও আশাবাদি হয়ে বাঁচতে চাই কিন্ত একটা কথা আমাদের ভুলে গেলে চলবেনা যে রুশ বিপ্লবের মহানায়ক লেনিনের স্বপ্ন বাস্তবায়ন হয়নি,বাস্তবায়ন হয়েছে গরবাচেভের স্বপ্ন!দুনিয়ার সর্বহারা মানুষের জন্য যে সোভিয়েত ইউনিয়ন প্রতিষ্ঠা করেছিলেন,  গরবাচেভের হঠকারী সিদ্ধান্ত সব ধ্বংস হয়েগেল! আজ সমগ্র পৃথিবীতে শাসনকরছে আমেরিকা! দুনিয়া আজ ভারসাম্যহীন।মনে রাখবেন যদি বাংলাদেশে সামপ্রদায়িক গোষ্ঠী ফনা তোলার সুযোগ পায় তাহলে কাউকে ছোবল মারতে দ্বিধাবোধ করবেনা। তাই ' সাদাকে সাদা আর কালোকে কালো বলার' সাহস আমাদের থাকা উচিৎ।",0,celebrity
"""আপুনি কে ??? আপনার নাম কি???"" স্যার খুবই মজাদার ঘটনা....",0,celebrity
১৯৭১এর কুলাঙ্গার এর বাচ্চাদের আচরন এর চেয়ে ভালো কেমনে হবে।।।ধন্যবাদ সার।। রাজাকারের মারার আগুনে ঘি দিলেন তাই।।।,0,celebrity
"এই পোষ্টে সবার কমেন্ট গুলো পড়লাম,,   অনকে অনেক রকম কথা বলেছে     তবে একটা বলতে পারি ইসলামকে কটাক্ষ করে  এসব মুক্ত চিন্তার কোন যোক্তিকতা যেমন নেই,,, তেমনি কাউকে হত্যা করে এর সুফল পাওয়া যায় না।  ইসলামকে প্রতিষ্টা করতে হলে, আগে ইসলাম ব্যাবসায়িদের  বিতারিত করতে হবে।",0,celebrity
"অভিজিত মুসলমান নয় , ইসলামি চিন্তাবিদ ও নয় , ওর মত নাস্তিক কে আল্লাহ উচিত শাস্তি দিয়েছেন ।। মুক্তমনা মানে  ধর্ম  কে অবমাননা নয় । অস্বাভাবিক ম্রীত্যু কারো কাম্য নয় । হত্যাকারী দের চরম শাস্তি  হওয়া উচিত ।",0,celebrity
"হর হর বমিবাজ,, বছর এর প্রথমদিন থেকে আলোচনায় থাকতে চান। সেই সাথে মিথ্যা এবং চাটুকারিতা প্রবহমান রাখতে চান হর হর বমির মত, তাইতো উনার ঝেটিয়ে স্ট্যাটাস।",0,celebrity
"স্যার ধন্যবাদ, লেখাটির জন্য, কিছু সত্য কথা উপস্থাপনার জন্য এই গুলি যে দূর্ঘটনা না হত্যা সেটা বলার জন্য দোষ বাস মালিকদের বেশী সেটা বলার জন্য মামলা হয় শুধু ড্রাইভারের বিরুদ্ধে কিন্তু সেটা ঠিক না কারন অাসল কালপ্রিট বাসের মালিক তার বিরুদ্ধেও মামলা হওয়া উচিত। সর্বশেষে বাংলাদেশের মানুষের কাছে অাপনি  কত ইমপোরটেন্ট তা এই ২/৩ দিনে বুঝা গেছে কারন অাপনার একটি মন্তব্যের জন্য অাপনার একটি লেখার জন্য বাংলার মানুষের সে কি হাহাকার। সেই জন্য অাপনার মত দিব্যি সুস্থ মানুষকে মেরে প্রযন্ত ফেলেছে। তবুও ভালো লেগেছে অাপনার প্রতি তাদের এই ভালোবাসা দেখে। তাদেরকে ধন্যবাদ তারা এত শিক্ষিত কিন্তু তাদের ভাষার প্রয়োগে যথেষ্ট নোংরামি ত্যাগ করতে না পারার জন্য।",0,celebrity
মদ খা মানুষ হঅ 😂,0,celebrity
ইকবালের মার্কা কি বা* ছাড়া আর কি।,0,celebrity
"মতিয়া চৌধুরী কেন যে তাদের ""রাজাকার "" না বলে ""কুত্তার বাচ্চা"" বলে নাই। তাহলে বুকে লিখতো ""আমি কুত্তার বাচ্চা।""",0,celebrity
এবং আশার বাণী হলো আগামী বছর থেকে আমরা বোকাচোদা রপ্তানি তে শীর্ষ স্হান পেতে পারি । হ্যাঁ ভাই হ্যাঁ । স্যাটেলাইট থেকে খবর পেলুম🐸,0,celebrity
"অসাধারন লিখেছেন, স্যার। পাশাপাশি মাদ্রাসা শিক্ষা বন্ধের জন্য কিছু লিখেন স্যার। এই দেশে স্যার হাজার হাজার মাদ্রাসা আছে - যেখান থেকে প্রতি বৎসর কয়েক লক্ষ ছাত্র- ছাত্রী বের হচ্ছে। অথচ এই মাদ্রাসার ছাত্র- ছাত্রীরা দেশের অর্থনীতিতে কোন অবদান রাখছে না। মাদ্রাসাগুলোকে কারিগরি শিক্ষা কেন্দ্রে রূপান্তর করার ব্যাপারে সরকার যাতে এগিয়ে আসে - সেজন্য কিছু একটা করুন স্যার। এই অপচয় ও বিনাশ মুলক মাদ্রাসা শিক্ষা দিয়ে কি হবে শুনি?  মাদ্রাসাগুলো  আমাদের জাতীয় অর্থনীতিতে কি ভুমিকা রাখছে - স্যার একটু ভেবে দেখবেন কি?",0,celebrity
"আমি এক গৃহযুদ্ধের মুখোমুখি দাঁড়িয়ে আছি।  সমূহ ক্ষতির ভয়ে হাতপা নাড়াচ্ছি না..  থানাকে তুমি পরিণত করেছ জল্লাদখানায়,  হাসপাতালগুলো ভরে গেছে কসাইয়ে ক্রসফায়ার আর গুমে দেশটাকে বানিয়েছ বধ্যভূমি।  তুমি আমার খাদ্যে ঢেলে দিচ্ছ বিষ, অথচ বলে বেড়াচ্ছ আমাকে খাওয়াচ্ছ মাগনা।  তুমি সব শিক্ষা দীক্ষা কেড়ে নিয়ে আমার  সন্তানদের ডাকাত দস্যু চোর লুটেরা  ছিনতাইকারী ধর্ষক বানাচ্ছ,  বলছ আমাকে শিক্ষা দিচ্ছ ।  তুমি তোমার কমিশনের জন্য আমার ঘরবাড়ি, চাষের জমি, মাছের নদী, লবণের মাঠ, বন তুলে দিচ্ছো বিদেশী বহুজাতিক বেনিয়াদের হাতে। আর এর গালভরা নাম দিয়েছ উন্নয়ন।  বিশ্ব বিদ্যালয়ে আমার সন্তানদের  শিক্ষার বদলে শেখাচ্ছ সন্ত্রাস। খাতা কলম কি বোর্ডের বদলে  তুমি হলের আলমারিগুলোতে সাজিয়ে রেখেছো  রামদা আর পর্ণোগ্রাফি।  আর কোটি কোটি জনগণকে তুমি  দাঁড় করিয়ে দিয়েছ গৃহযুদ্ধের সামনে। আমার সন্তানদের পিছে লেলিয়ে দিয়েছ আমার সন্তানদের। আমার সন্তানদের দিয়ে ধর্ষণ করাচ্ছ আমার মেয়েদের। তুমি এর নাম দিয়েছ প্রতিরোধ ?  ব্যাংক থেকে আমার হাজার কোটি টাকা  লোপাট হয়ে যায় তুমি চুপ।  রিজার্ভ ব্যাংকের বিলিয়ন ডলার চুরি হয়ে যায় তুমি চুপ।  শেয়ারবাজারের ক্ষুদ্র জামানতকারিদের  কাগজগুলো খেয়ে ফেলে তোমার গৃহপালিত উইপোকা তুমি চুপ।   একটি গৃহযুদ্ধের মুখোমুখি দাঁড়িয়েও আমি চুপ হয়ে আছি হাতপা নাড়াচ্ছি না ...  সমূহ ক্ষতির ভয়ে।  অথচ ক্ষতি যা হবার তা হয়েই যাচ্ছে হরদম  তুমি চেপে ধরেছ আমার কন্ঠনালী,  তুমি কেড়ে নিয়েছ আমার ব্যানার, তুমি কেড়ে নিয়েছ আমার লেখার খাতা ও কলম। আমার অব্যক্ত কথাগুলো বলার জন্য  তুমি আমাকে কোথাও দাঁড়াতেই দিচ্ছনা। আমার সমস্ত কথা বলার, প্রতিবাদ জানানোর ভাষাকে তুমি হত্যা করছ প্রতিদিন।  আর এর নাম দিয়েছ তুমি বাক-স্বাধীনতা। আর ক্রমশ ঠেলতে ঠেলতে আমাকে তুমি দাঁড় করিয়ে দিয়েছ গৃহযুদ্ধের মুখোমুখি।",0,celebrity
"বাংগালীকে কুলাঙ্গার বানাইয়া রেখেছেন আর এখন চাচ্ছেন অন্ধ্য বানাইতে?... আপনার লেখা ও আপনাকে দেখলে  পুরাই মীরে জাফরের বংশধরের মত লাগে। পালানোর রাস্তা পাবেন না,😡..বাংলাদেশের স্টুডেন্ট কুলাঙ্গার? 👿...  কি ভাবছেন?.",0,celebrity
"Yes, you are right sir (Y)",0,celebrity
স্যারের জন্য শুধুই ভালবাসা........,0,celebrity
এসো হে বৈশাখ এসো একসাথে কমেন্ট পড়ি Umme Salma Mitu,0,celebrity
yes sir,0,celebrity
"জাফর ইকবাল স্যার, শুনলাম কিছুদিন আগে পাবনা থেকে একজন ডাক্তার এসেছিল আপনার বাড়িতে বেড়াতে, কি কারণে, কেন এসেছিল তাতো আর আমরা জানি না।  স্যার আবার ঐ ডাক্তার কে ডেকে আনেন, এবার আসার পর জামাই আদর করে পোলাউ, মাংস, একটু বেশি বেশি খাওয়া ডাক্তার বাবু কে বলুনঃ  ডাক্তার মশাই এর আগেরবার কি ডোস দিলা সেই যেই, এবার একটু চিকিৎসাটা ঠিক মতো করো ডাক্তার মশাই",0,celebrity
অসাধারণ স্যার.......,0,celebrity
স্যারে নাকি কমেন্ট পড়েন না!স্যারের হয়ে আমিই কমেন্টগুলা পড়তে আইছি!কমেন্ট পড়তাছি আর ভাবতাছি অনেক দিন বাঁচসি আর নাহ...#বিদায়_পিত্তিবি।।,0,celebrity
আপনি ভালোবাসা ♥♥,0,celebrity
এখন তো কোনটাই নাই।,0,celebrity
"স্যারের মনে হয় পাতলা হাগু হইছে, কদিন আগে বমির বেরাম, মাথা ও ঘুন্টি দিতাছে না স্যার??",0,celebrity
"অভিজিৎ তুমি মোদের ক্ষমা করো, একটা স্বাধীন দেশে একজন স্বাধীনমনা মানুষকে ওরা বাঁচতে দিলো না------!!!",0,celebrity
"স্যার,আপনার ঘুম ভাঙ্গালো কেডাই?আপনি ঘুমের দাওয়াই খাইয়া ঘুমাইছিলেন না?",0,celebrity
"আপনি তারাতারি সুস্থ হোন,, এই কামনাই করি,,",0,celebrity
আন্তর্জাতিক দালাল,0,celebrity
জাফর-ইকবাল বাবুর হাহা React পাওয়াটা একটা সার্থকতা।,0,celebrity
অবশেষে আপনার ঘুম ভেঙ্গেছে!!!,0,celebrity
"ইমতিয়াজ আজাদ ভাই, কেমন আজব লাগে যেন এদেশের মানুষদের। আচ্ছা, ধরলাম জাফর ইকবাল আম্লীগের লোক। বাট ইশতেহার গুলোতে যা লিখা আছে তার বাইরে কিছু লিখা নাই, আপনিই বলেন কার ইশতেহার কতটা ভাললাগছে?  জামাতকে সাথে নিয়ে যুদ্ধপরাধীদের বিচার বহাল থাকবে এটা পড়ে আপনি কি শিহরিত না?😆",0,celebrity
আমরা কি প্রথমা প্রকাশনীর কাছ থেকে এই বই প্রস্তুত করা সংক্রান্ত একটা পূর্ণাঙ্গ রিপোর্ট পেতে পারি? আমাদের মনের শান্তনার জন্যে?,0,celebrity
"কে তুমি বৎস, ধরিয়া মৎস, বেচিয়া গঞ্জে, অকুল ও কুঞ্জে, না খাইয়া তাজা, কেনো ভক্ষন করিয়াছো মেয়াদ উত্তীর্ণ গাজা(2) 😂😂",0,celebrity
"You are great,sir.",0,celebrity
মনে হয় স্যাড় কোমায় চলেগিয়েছিলেন।,0,celebrity
অামি বিশ্বাস করি অাপনি মাথায় অাঘাত পেয়েছেন,0,celebrity
"লেখার আগাগোড়া কিছুই পড়ি নাই।আমি জাস্ট কমেন্ট গুলা পড়তে আইছি।এখন কি আমার বমি চলে আসতে পারে? 😜 আসলেই কি,আসুক।আমার সেফুদা আছে না।আমি তখন মদ খাবো....... 😜😜",0,celebrity
"কমেন্টগুলো দেখলে বিশ্বাস হয়, বাংলাদেশে এখনও কত নির্বোধ অর্বাচীন।",0,celebrity
"যারা মুক্তিযুদ্ধের চেতনার কথা বলে, চেতনা নিয়ে রাজনীতি করে তারা হলো সবচাইতে বড় দালাল । মুক্তিযোদ্ধার চেতনা দিয়ে এখন দেশ চলে না, এখন পেক্ষাপট সম্পূর্ণ ভিন্ন । তখন আমাদের শত্রু পক্ষ কারা সেটা স্পষ্ট ছিল কিন্তু এখন আমরা নিজেরাই নিজেদের প্রতিপক্ষ, নিজেরাই নিজেদের ক্ষতি করতে চাচ্ছি । চেতনা নিয়ে রাজনীতি বন্ধ হোক, যারা চেতনার কথা বলে তাদেরকে বয়কট করা হোক ।",0,celebrity
চান্দু কই আছিলা? হ্যা?😜,0,celebrity
"শহীদুল আলমের দুরবস্থায় আপনি কষ্ট পেয়েছেন, সেটা মানবিক। কিন্তু ফেসবুকে এই লেখাটি দেবার পর আপনি কি কমেন্টগুলো পড়েছেন? যদি পড়েন, তাহলে অনুধাবন করতে পারবেন কেন তাকে আটক করা হয়েছে!",0,celebrity
দাদু আমারে মাফ কইরা দিয়েন আমি ভুলে আপনার গায়েবানা জানাযায় অংশ গ্রহণ করছি। ক্ষমা চাচ্ছি দাদু।  এখন আমার খুব হড়হড় করে বমি হচ্ছে। বাঁচবো কিনা সন্দেহ। আচ্ছা সিলেটে বাতাবি লেবুর ফলন কেমন হচ্ছে দাদু????,0,celebrity
একে অপরের পাশে থেকে কি-ই বা করতে পারছি। সান্তনা ছাড়া। খুব রাগ হয়। অথছ কিছুই করতে পারি না। কিছুই করা হয়ে ওঠে না।,0,celebrity
অনেক তথ্য বহুল এবং মজার বিষয় যা গনতন্ত্রগামী বাঙ্গালীকে সঠিক পথ দেখাতে পারে |,0,celebrity
তৈলাক্ত পোস্ট .. Saykat Roy,0,celebrity
এই বালের কলিজা নিয়া আপনি কিশোরদের সাহসী হওয়ার গল্প লিখেন..??  আপনার মতো বলদ থেকে শিক্ষা নেওয়া জাতি আর কি শিখবে বলেন...,0,celebrity
"শিক্ষা ক্ষেত্রে অাপনি মনে হয় একটাই কল্যাণকর দাবী করে অাসছেন, অার তা হলো সমন্বিত ভর্তি পরিক্ষা। অাশা করব এ ব্যাপারে অাপনি অারো জোরাল দাবী জানাবেন।",0,celebrity
এই বইটার দাম কত এবং এর নাম কী?,0,celebrity
"আপনার বিলম্বিত উপলদ্ধির জন্য অনেক ধন্যবাদ৤ ফেল না করানো, বানান কিংবা বাক্য গঠনে ভুল হলে মার্ক কাটা যাবেনা বলে শিক্ষা মণ্ত্রণালয়ের আদেশ আর কেন্দ্রে যেভাবে নকল করার উত্‌সব দেখা গেল তা নিয়ে কিছু বলবেন আশা করি৤ আমরা অনেক আগে থেকেই সাবধান করছিলাম যে, অমাদের শিক্ষানীতি ধ্বংসের মাধ্যমে আমাদের ভবিষ্যত্‌ প্রজম্মকে অক্ষম, অধম, অথর্ব ও জ্ঞান গরিমাহীন একটি জাতিতে পরিণত করার কাজ প্রায় সম্পন্ন করা হয়েছে তথাকথিত উন্নয়নবাদীগণ কতৃক আর তখন আমাদের বিভিন্ন বিশেষণে ভূষিত করা হল৤ আর এখন ? সবাই যদি এখন থেকে সোচ্চার না হই আর প্রতিরোধ না করি, তাহলে আমাদের আগামী প্রজম্ম নির্ঘাত অন্ধকারে নিমজ্জিত হবে৤",0,celebrity
"এতো ক্ষনে তার ঘুম ভাঙলো।ঘুমের ঘোরে চোখ কচলাতে কচলাতে লেখা তার উপন্যাসটি মোটেও জুতসই মনে হচ্ছে না (মন ভরছে না)। আপনি চাইলেই এক বা দুই লাইনেই আমার মত অনেকর  মন ভরাতে পারতেন। যা হোক মাত্র উঠলেন,মুখটা ভালো করে ধুয়ে মন ভরানোর মত কিছু করা যায় কিনা সেটা করেন স্যার।",0,celebrity
অধ্যাপক ড.জাফর ইকবালের উপর যখন হামলা হয়েছিল তখন ছাত্ররা সারাদেশব্যাপি আন্দোলন করেছিল। হামলাকারীর দৃষ্টান্তমূলক শাস্তির দাবীতে ছাত্রসমাজ মাঠে নেমেছিল।  আজ কোটা সংস্কারের দাবীতে আন্দোলনরত ছাত্রছাত্রীদের উপর পুলিশের নগ্ন হামলার প্রতিবাদে তিনি কিছু বলেছেন?  খুব জানতে ইচ্ছা করছে :) #Reform_Quota,0,celebrity
উস্কানি মূলক পোস্ট । রিমান্ডের দাবি জানাচ্ছি ।,0,celebrity
"জাফর ইকবাল হল গভীর  জলের মাছ। আন্দোলনের সুরু থেকেই উনি,  সবকিছু পর্যবেক্ষন করেছেন। নীরবে দেখেছেন সরকারের মতামত কি। ছাত্র-ছাত্রীদের অবস্থা কি। দেখেছেন জল কোনদিকে গড়ায়। তারপর সুযোগ বুঝে একটা লেখা প্রকাশ করলেন। আজ যদি আন্দোলন সফল হতো, পজিটিভ ফলাফল আসতো, তখন উনি ""অন্যরকম একটা পোস্ট দিতেন""।  উনি মুক্তিযুদ্ধ নিয়ে আবেগী লেখা লিখলো, অথচ নিজে জিবনেও যুদ্ধ করে নাই। যাত্রাবাড়ীতে গর্ত করে থেকেছে। উনার মুখে এসব মানায় না। উনার লিখার দক্ষতা অসাধারন, তাই যেটাই লিখবে সেটার প্রভাব পড়বে সবার মধ্যে। তবে তিনি সেটাই লিখে থাকেন যেটা নিজের জন্য ভালো। উনি ন্যায়ের কথা লিখেননা, স্বার্থের কথা লেখেন। উনি স্বার্থান্বেষী ভীরু কাপুরুষ, উনি কারো জন্য প্রাণ দিতে জানেননা,",0,celebrity
আহা! আহা! জেগেছেন! জেগেছেন অতঃপর স্যারের ঘুম ভেঙ্গেছে স্যারের জন্য চায়ের ব্যবস্থা করেন প্লিজ😉,0,celebrity
"খুবই দুঃখজনক ব্যাপার যে কেন ওরা রাজাকার লিখে রাস্তায় নেমেছিলো সেটা আপনার মতো জ্ঞানি মানুষ বুঝতে পারেনি, আপনি বরং মতিয়া চৌধুবীরে জিজ্ঞেস করুন। আপনার কিশোর উপন্যাস আর সাইন্স ফিকশন পড়ে আপনার মোটামোটি একজন ভক্ত আমি, মতিয়া খালা যখন সবাইকে রাজাকারের বাচ্চা বলে গালি দিছিলো আন্দোলনের জন্য তখন কি আপনি উগান্ডা ছিলেন? লাস্ট কথা আপনি হুমায়ুন স্যারের ভাই হয়ে এরকম কমবুদ্ধি নিয়ে বেচে আছেন ভাবতেই খারাপ লাগে জনাব। আর মুক্তিযুদ্ধ আমরা দেখিনি তবে তা সম্পর্কে পরাশোনা করেছি, সবার রক্তেই ৭১এর তাৎপর্য প্রবাহমান। এট লাস্ট আপনার মতো মহৎ ব্যাক্তিকে একটাই কথা বলতে চাই ফেসবুকে ভাঁড়ামি না করে সাহিত্যে মন দেন, সবখানে মুক্তিযুদ্ধের নামে আওয়ামিলীগরে সাপোর্ট করলে (আমার ফ্যামিলিও আওয়ামী সাপোর্টার) রাজনীতিতে যোগ দিতে পারেন। ধন্যবাদ :-)",0,celebrity
"আপনি ফ্যাসিস্ট আওয়ামী লীগের একজন সমর্থক ও বুদ্ধিজীবি হিসেবে আমি আপনার ফ্যাসিস্ট সাপোর্টিং লেখা কলাম গুলোর তীব্র বিরোধী । আমি প্রায়ই আপনার বিরুদ্ধে কলম ধরে ফেইসবুকে ব্যাবচ্ছেদ করি । কিন্তু আপনার উপর এই হামলা আমি মেনে নিতে পারিনি , আপনার উপর হামলাকে  তীব্র নিন্দা জানানোর কারণে অনেকই আমাকে টিপ্পনি কেটেছে ।কিন্তু আপনার সুস্থতা কামন করছি । আবার ফিরে আসুন এবং লিখুন ! আর আমিও প্রস্তুত হচ্ছি আপনার মতামতের সমালোচনা করার জন্য ।",0,celebrity
স্যার আপনি  ভালো-মন্দ যাই লিখুন না কেন ইদানিং আপনার লেখা পড়লে কেমন জানি হড়হড়িয়ে বমি চলে আসে।,0,celebrity
"জাফর ইকবাল স্যারকে নকল করে যারা বিখ্যাত হয়েছেন!! সাল সহ, মনোযোগ দিয়ে পুরা পড়ুন। আপনি ‘অবনীল’ নামক একটি বই প্রকাশ করেন ২০০৪ সালে। আর বইটি হবুহ নকল করে ২০০০ সালে জিম হুইট আর কেন হুইট নামে দুই ভাই মিলে “পিচ ব্লাক” নামে একটি হলিউডের সিনেমা বানিয়ে ফেলেন। আপনি ১৯৯৯ সালে ‘নিতু তার বন্ধুরা’ নামক আরেকটি বই লেখেন। আপনার এই বইটা নকল করে দানি দেভিতো নামে এক ভদ্র লোক ‘ম্যাটিল্ডা’ নামে এক হলিউডের সিনেমা বানিয়ে ফেললেন ১৯৯৪ সালে‍! ছবিটি বাজেটের চেয়ে ৬৫ কোটি ডলার বেশি নিজের পকেটে ঢুকিয়েছেন অথচ আপনাকে একটি টাকাও দিলেন না!! আপনার ২০০৫ সালে বের হওয়া ‘আমি তপু’ ১০ বছর আগে ১৯৯৫ সালে ডেবিড পেলজার নামে আমিরিকান এক সাহিত্যক নকল করেন। তার বইটির নাম দেন ‘আ চাইল্ড কল্ড ইট’। আপনার ২০০০ সালে বের হওয়া ‘মেকু কাহিনী’ বইটি নকল করে ১৯৯৪ সালে প্যাট্রিক রিড জনসন নামে এক হলিউডের পরিচালক বানিয়ে ফেললেন বিশ্ব বিখ্যাত শিশুতোষ ছবি ‘বেবিজ ডে আউট’। একই ভাবে আপনার ১৯৮৮ সালে ""ট্রাইটন একটি গ্রহের নাম"" বইটি নকল করে ১৯৭৯ সালে বের করা হয় ‘এলিয়ন’ নামের বিশ্বসেরা সায়েন্স ফিকশনটিও। collected",0,celebrity
"কমেন্ট পড়ে যা দেখলাম, দেশেতো বেজন্মা বিজাত (বিএনপি জামাত) আবালের সংখ্যা নেহাত কম না.... হায়রে মেদাবী!!!",0,celebrity
অসমাপ্ত আত্মজীবনী |,0,celebrity
"Muhammed Zafar Iqbal স্যার আপনার লিখাটা আমি মনোযোগ দিয়ে পড়েছি। আপনি অনেক কথাই বলেছেন। এর মধ্যে একটা কথা হল “আমি আসলে ফেসবুক, নেট, ব্লগের সাথে পরিচিত নই” তবে আপনি কেন অভিজিৎ কে নিয়ে লিখতে গেলেন। আপনি কি মনে করেন যে অভিজিৎ কে কোন সাধারণ কারণে হত্যা করা হয়েছে? আপনার লিখা বই আমার ভাল লাগে তাই আম পড়ি। কিন্তু আপনি তার আড়ালে যদি একটা বিশেষ গোষ্টিকে কটাক্ক করে কথা বলেন তবে কি আপনাকে ঠিক একই ভাবে সবাই পছন্দ করবে?? আমি ঠিক বুঝি না আপনারা যারা এখনকার তথাকথিত বুদ্ধিজীবী আছেন তারা কিভাবে কোন কিছু না জেনে কথা বলেন। আপনাদের কি উচিৎ নয় সব কিছু ভাল ভাবে জেনে কথা বলা? আপনি জঙ্গি কথাটা কয়েকবার ব্যাবহার করেছেন। আপনি জঙ্গি বলতে কি বুঝাতে চেয়েছেন তা কিন্তু পরিস্কার করেন নাই। আসলে আপনার ধর্ম কি এইটাও কিন্তু পরিস্কার না। একজন মানুষ হত্যা করা অন্যায়, অপরাধ এবং চরম ভাবে ঘৃণিত কাজ। আমি ব্যাক্তিগত ভাবে কখনোই এই কাজটা সাপোর্ট করি না। কিন্তু একটা কুকুর যদি পাগল হয়ে যায় তখন তাকে মেরে ফেলতে হয় তা না করলে মানব সমাজের ক্ষতি হওয়ার আশঙ্কা থেকে যায়। আমি একটা কথা বলেছি আপনার ধর্ম কি এটাও কিন্তু পরিস্কার না। মেনে নিলাম আপনি কোন ধর্মের ফলোয়ার না। এর মানে তো এই হতে পারে না আপনি আরেকজনের ধর্মীয় অনুভূতিতে আঘাত করবেন? আপনি কি এটাকে সাপোর্ট করেন? আশাকরি আপনি এই ব্লগের লিখাগুলো পড়ে আপনি এই অভিজিৎ সম্পর্কে গঠন মুলক সমালোচনা করবেন। http://mukto-mona.com/bangla_blog/?p=16137",0,celebrity
আপনার ভিড়িওটির শিরোনাম আছে বাংলাদেশের কোন নায়িকা রাত কাটাতে কত টাকা নেনআপনার মুল ভিড়িওতে আছে ছবিতে কত টাকা নেয়শিরোনাম আর ভিড়িও রাত দিন তপাতআমার কথা হলে মিথ্যা কথা বলে ভিড়িটি দেখার জন্য মা বাবাকে কেন গালি শুনানএই ভিড়িওতে আপনি কত টাকা পাবেনমা বাবাকে গালি শুনাতে খুব ভাল লাগে তাই নাতোদের মতো মাগিদের কারনে ইউটিব নষ্ট হয়ে গেছেমাগির বাচ্ছা তোর দাম কত বল পুটকি দিয়ে জনগন চুদবে,0,"Meme, TikTok and others"
অপু আপুকেই দেখতে চাই,0,"Meme, TikTok and others"
কিই ছবি দেছো মাগিরা তোগো কারনেই মানুষের আজ এ অবস্তা,0,"Meme, TikTok and others"
এই কথা গুলা একদম সত্যি বলছ নিচয় রিফাতের সাথে মিন্নি ডাইনির বেজাল দন্ড ছিল তাই এসব গটিয়েছে,0,"Meme, TikTok and others"
বুবলী খান বিউটিফুল,0,"Meme, TikTok and others"
কিছু বলার নাই এইসব জানয়ারদের ফাসি হওয়া দরকার,0,"Meme, TikTok and others"
নিতে পারেন,0,"Meme, TikTok and others"
আমি সাকিবের সাথে এক মত,0,"Meme, TikTok and others"
আমেরিকা আর বাংলাদেশের সংস্কৃতি এক না,0,"Meme, TikTok and others"
পাবলিক কে বার্কছিস,0,"Meme, TikTok and others"
উগ্রপন্থা এসব কথা পাইলি কই সে কি উগ্র পৃথিবীর বুকে অমুসলিমরা অগ্রগতি হাজার হাজার মুসলিমদেরকে হত্যা করতেছে সেইসব কেউ কারো নয় পৃথিবীর বুকে এখন ওদের দালাল ভরে গেছে,0,"Meme, TikTok and others"
বালের ভিডিও ফাস,0,"Meme, TikTok and others"
তোরা হাঁষ দেখছু,0,"Meme, TikTok and others"
আমি সবার কাছে প্রশ্ন রাখি মুয়ুরির ছবি তার ছেলে মেয়ে দেখে কি শিখবে আল্লাহ সবাইকে বুজার তওফিক দান করুকআমিন,0,"Meme, TikTok and others"
চোখের পানি ধরে রাখতে পারলাম না এমন সন্তান জন্ম হওয়ার থেকে সারাজীবন নিঃসন্তান থাকা ভাল আল্লাহ নিশ্চয়ই হাসরের মাঠে এর কঠিন থেকে কঠিনতম বিচার করবেন,0,"Meme, TikTok and others"
ওকে জুতা পেটা করা উচিত৷ শুধু তাই নয়,0,"Meme, TikTok and others"
আপনার ইমু নাম্বার দেন,0,"Meme, TikTok and others"
ওকে ফাঁসি দেওয়া চাই,0,"Meme, TikTok and others"
সব ঝামেলার গোড়া ওনার মেয়ে,0,"Meme, TikTok and others"
সময় টিভি ভাই এইটা কি বাংলাদেশর না অন্যদেশের ঘটনা একটু বলবেন,0,"Meme, TikTok and others"
টাকা আমিদেবনংভারদাও,0,"Meme, TikTok and others"
তার আশা পুরন হক,0,"Meme, TikTok and others"
শালার দুধ,0,"Meme, TikTok and others"
আল্লাহ সবাইকে হেদায়েত দান করুক,0,"Meme, TikTok and others"
ময়ুরি সবার সেরা,0,"Meme, TikTok and others"
এরকম ভিডিও আরো দেখতে চাই,0,"Meme, TikTok and others"
পাকিছথান কাসমির আলহামদুলিল্লাহ,0,"Meme, TikTok and others"
ভালো বাসি তোমাকে এই বিশেষ আই লাভ এই,0,"Meme, TikTok and others"
বাবা কথা শুনতে শুনতে মনে জয় ভালো বাসে বেশি বেশি,0,"Meme, TikTok and others"
মনে হচ্ছে ওখানে গিয়ে শালার হাত ভেঙে দিয়ে আসি এত বড় বেইমান সন্তান এই শালা,0,"Meme, TikTok and others"
শয়তানের দল ভারি,0,"Meme, TikTok and others"
মোটা গুলোর মাপ সঠিক হতে পারে কিন্তু নতুন নায়িকাদের সবগুলোর মাপ ভুল বলা হয়েছে তাদেরকে করে রাখার জন্য অদ্ভুত মিথ্যা কথা কোমর সাইজ জাতি এখন ডিজিটাল বোকা বানানো যাবে না,0,"Meme, TikTok and others"
নারায়ে তকবিরআল্লাহু আকবার বাংলাদেশ হতে কোটি কোটি মুজাহিদ যুদ্ধে যাবেমালাউন ভারতের শেষ দেখে ছাড়বোকোন রক্তই বৃথা যাবেনাআমাদের পুরস্কার আল্লাহর কাছে,0,"Meme, TikTok and others"
ঐশ্বরিয়া,0,"Meme, TikTok and others"
ওরে রাস্তায় দাড়া করাই পেট্রল দিয়া আগুন দিয়াজ্বালাইয়া দিতে হয়,0,"Meme, TikTok and others"
তোমরা এক টা কাজ করতে পারো ওকে মেরে ফেলুন,0,"Meme, TikTok and others"
ওর কপাল ভালো জে বাংলাদেশের না তাইলে মাটির নিচে থাকতো ও,0,"Meme, TikTok and others"
পূজা চেরি কে সেই লাগে,0,"Meme, TikTok and others"
আমি চাই যেখানে মসজিদ ছিল সেখান থাকে দুরে মন্দির তৈরি করুন না সরকারের অনেক টাকা তো যেখানে টাউন নেই সেখানে টাউন করুন না অয়্যোধায়,0,"Meme, TikTok and others"
তারা তারি চালু হোক,0,"Meme, TikTok and others"
আমি বলবো এটা সামাজিক অবক্ষয় অতি লোভ লালসা থেকে এগুলোর উৎপত্তি খুব করুন,0,"Meme, TikTok and others"
আমার নবীর নিয়ে কিছু বল্লে তোরে দেশে পাইলে কুত্তা দিয়া কাম করাবো,0,"Meme, TikTok and others"
আমিও এক মত সানাই কে মিডিয়া থেকে বাদ দেয়া হক ও নারী জাতির কলংক ছি ছি ছি,0,"Meme, TikTok and others"
হয়,0,"Meme, TikTok and others"
আমি ও চাই নতুন একটা সম্পর্ক করতে কিন্তু এখন ভালো কোনো বন্ধুই পাওয়া যায় না,0,"Meme, TikTok and others"
যারা জাকির নায়েকের মিথ্যাচার করবে তারা সয়তান ও কাফের,0,"Meme, TikTok and others"
ওরে আমি পাইলে কি যে করতাম রে,0,"Meme, TikTok and others"
আপনার ভয়েস না আর কিছু,0,"Meme, TikTok and others"
আমরা একা কুরবানি দেই তাই হাজার টাকা দিয়ে একটি গরু কিনছি জে জে হাজার টাকার গরু কিনছেন একটি করেদিয়ে দেন আমি খুব গরু কিনে আমার কাছে গরুটা ভাল লাগছে দোয়া করবেন জাতে পরের ঈদে আরও বড় গরু কিনতে পারি,0,"Meme, TikTok and others"
সত্যিই আমি কেঁদে ফেলেছি,0,"Meme, TikTok and others"
তোমার খুব খাুউজানি আছে আমার কাছে ঔষধ আছে নিবে নাকি,0,"Meme, TikTok and others"
আমার বাড়ি দীঘা,0,"Meme, TikTok and others"
আমি মোদির আইনের বিপক্ষে মোদির এই আমি মানি না মোদী হালার কপালে জুতা মারো,0,"Meme, TikTok and others"
কি বলবো আল্লাহ তুমি এই সব মানুষদের হেদায়াত করো,0,"Meme, TikTok and others"
এতো মুরব্বি একজন লোক কে এভাবে মারলোচেলে হয়ে বাবা কে হিন্দু ধর্ম হলে কি হলো মহান পাক রাব্বুল আলামিন তো আছেন তিনি তো সব দেখতেছেন তাই তো উনার উচিটার শিক্ষা হয়েছে,0,"Meme, TikTok and others"
আপু আমি আপনার চ্যানেলটি সাবস্ক্রাইব করলাম,0,"Meme, TikTok and others"
তোমাতের কি এত কেন জলে,0,"Meme, TikTok and others"
বাবুল সুপ্রিয় মত আসাউদ্দিন ওয়াসি বাগাল নয় বাবুল সুপ্রিয় ওর পায়ের নখের যোগ্য হতে পারবেনা,0,"Meme, TikTok and others"
ভগবানের চাকর আর দূতের মধ্যে কি পার্থক্য একটু বলবে,0,"Meme, TikTok and others"
আল্লাহ আপনে এমন সন্তান কে হেদায়েত করুন,0,"Meme, TikTok and others"
আল্লাহ তুমি তার চরম বিচার করোতাকে তুমি এই দুনিয়ায় ও আখিরাতে তার বিচার করোতার ছেলে ও তাঁকে এর চেয়ে বেশি মার ধর করে এবং তার ওই দাজ্জাল বউকে ও যেন মারে৷ আমার গুনাগারের দোয়া কবুল করো৷,0,"Meme, TikTok and others"
মুসলমানদের প্রতি অবিছার করছে মুদি সরকার,0,"Meme, TikTok and others"
তোমাকে ল,0,"Meme, TikTok and others"
আমারে দয়া করেঔ সালার নামবার টা দেন কেও ওরে আমি জবাই করবো ও আমাদের বাবার বয়সে লোকের গায়ে হাত তুলছে আমার গাঁ টা এখন গরম হয়ে গেছে ওরে জবাই করতে মন চায়,0,"Meme, TikTok and others"
আমি চাই পাকিস্তান আর অন্যান্য মুসলিম দেশ মিলে ভারতকে হাজার ভাগে ভাগ করে দেক আর মোদির ভারত ভাইঙ্গা দেক,0,"Meme, TikTok and others"
এই আইন মানিনা মানবোনা,0,"Meme, TikTok and others"
হে আল্লাহ এই জানয়ার কে জমিনে ধসায়ে দেন,0,"Meme, TikTok and others"
আমরা মজদি ফেরত চায়,0,"Meme, TikTok and others"
আমি চাই দিদি মদি গুণডা চোৱ,0,"Meme, TikTok and others"
সব ঘটনার মুলে রয়েছে মেয়েটা,0,"Meme, TikTok and others"
ঠিক আছে ওই ছেলেকে ধরে আর বৌ কে ধরে জেলে দেওয়া হোক,0,"Meme, TikTok and others"
বাবরি মসজিদ ছিল আছে থাকবে ইনশাআল্লাহ,0,"Meme, TikTok and others"
কুওার বাইচ্চারা,0,"Meme, TikTok and others"
কনো কথা হবেনা সরাসরি ওর ফাঁসি চাই,0,"Meme, TikTok and others"
এমরান কেধন্যবাদ,0,"Meme, TikTok and others"
আপনাদের কারনে আজ আমরা একজন জানোয়ারকে দেখতে পেলাম তার হাত কেটে নেয়া হক,0,"Meme, TikTok and others"
কালি ডোভাই সয়তান না বড়ো সয়তান বাংলাদেশ,0,"Meme, TikTok and others"
ভিখারি রা ভিখারি থেকে,0,"Meme, TikTok and others"
আপুকলদায় ইমু,0,"Meme, TikTok and others"
একটা মেয়ে চাই ইম,0,"Meme, TikTok and others"
খুব বালো লাগে,0,"Meme, TikTok and others"
এমন ছেলে মেরে ফেলা ওচিত পুরটা দেখতে পারলামনা চখে পানি চলে আসলো আল্লা অকে মাপ করবেনা,0,"Meme, TikTok and others"
অনেক দিন শাকিব অপুর ছবি দেখিনা শাকিব অপু এক হলে তো ইন্ড্রাস্টির পক্ষে খুব ভাল হবে এবং আমরা শাকিবিয়ান রা খুব খুশি হবো,0,"Meme, TikTok and others"
সালাহ উদ্দিন কাদের একজন ভালো মানুষ এবং সে একজন বাঘের বাচ্চা ছিলো যারা তাদের বিরুদ্দে বলে আসলে তাদের জন্মের দোষ আছে,0,"Meme, TikTok and others"
আপনার মাথায় দুষ না কি যে ভারতের পক্ষে ভোট দিব আপনারা দেখেন না কি হারে ভারতে মুসলিম হত্যা করা হয় এতদস্বত্বে জানতে চাইছেন কার পক্ষে পাকিস্তানের পক্ষে কি হয়েছিল সালে তা আর জানতে চাইনা দুনিয়ার সবাই ভাল কেবল আমি বাদে,0,"Meme, TikTok and others"
মোহাম্মদ বিন সালমান ইহুদির দালাল জামাল খাসুগির কুনি মোহাম্মদ বিনসালমান,0,"Meme, TikTok and others"
আমি বলি কেন এরকম লেকবেন বুবলি সে নিকেকে ওনেক বর মনে করে,0,"Meme, TikTok and others"
বালের বক্তব্য ফালতু দেশে ফালতু রাষ্ট্রপতির ফালতু বন্তব্য,0,"Meme, TikTok and others"
জদি এই টা বাংলাদেসে জদি আমার চোখের সামনে হতো তাহলে ওর দুই হাত আর দুই চোখ তুলে ফেলতামআইনে তোয়াকা করতামনা,0,"Meme, TikTok and others"
কোথায়,0,"Meme, TikTok and others"
শাকিবঅপুএকহয়েসংসারকরুক,0,"Meme, TikTok and others"
ভায়নামাজ নিয়া বাজে কথা বলিয়েননা পিলিজজজজজ,0,"Meme, TikTok and others"
ছেলের সাথে তার বউকে নেওয়া উচিত,0,"Meme, TikTok and others"
সন্তানের কথা ভেবে ওদের দুজনের এক হয়া উচিত,0,"Meme, TikTok and others"
এগুলা দেখে কি বলব আমি জানি না,0,"Meme, TikTok and others"
সৌদি যুবরাজ এর পদক্ষেপ সংক্রান্ত নিউজ কোথায় মিথ্যে সংবাদ প্রচারের জন্য তথ্য প্রযুক্তি আইনে তোমাদের বিরুদ্ধে আইনানুগ ব্যবস্থা নেয়া হবে,0,"Meme, TikTok and others"
হায় হায় এ কেমন ছেলে,0,"Meme, TikTok and others"
ওর কপালে বেহেস্তে নাই আল্লাহ যেন জাহান্নাম বাসি করুক এমন ছেলেকে,0,"Meme, TikTok and others"
ওরে একদম ঐখানেই ছুলাইয়া ফেলতাম আমি থাকলে,0,"Meme, TikTok and others"
ভারত সুপ্রিম কোটের প্রধান বিচারপতি রঞ্জন গৈগ অবসরে যাওয়ার আগে মোদি সরকার থেকে মোটা অঙ্কের অর্থ হাতিয়ে নিয়ে বিতর্কিত মসজিদের স্থানে মন্দির করার রায় দিয়েছে আল্লাহ্রর নালত রঞ্জন গগৈগের উপর তার ধংশ অনিবার্য ইন শা আল্লাহ্ ঈমাম বুখারি ও সালমানের বাবা যা বলছে তা একান্তই তাদের নিজস্ব মতামত আমরা মুসলমানরা কোন দিনও মেনে নিব না আর তসলিমা নাসরিনের অন্তরের দৃষ্টি শক্তি মহান আল্লাহ্ অন্ধ করে দিয়েছে এবং সে শয়তান ধারা পরিচালিত ও বরবাদীদের অন্তর ভুক্ত হয়েছে সে তার অন্তরের দৃষ্টি শক্তি হারিয়ে এখন পাগলের প্রলাপ বলছে আল্লাহ্রর ঘর ভেঙে সেখানে দক্ষ লক্ষ ইবলিশের ইবাদত খানা তৈরি করতে যারা সমর্থন করে তাদেরকে আমরা উগ্র সন্ত্রাসী কুসেডারার হিন্দুত্ব বাদীদের মতই চিন্তিত করিয়াছি এবং মহান আল্লাহ্রর দরবারে কঠিন বিচারের জন্য পার্থনা করিতেছি বাকি সবই মহান আল্লাহ্ ভাল জানেন,0,"Meme, TikTok and others"
চিন্তা করিস নাতুই তর বাপেরে যেভাবে মারছিস ঠিক সেভাবে তর ছেলে তরে মারবে এর চাইতে বেশি মার তর ছেলে তরে মারবে,0,"Meme, TikTok and others"
জিনিসটা জটিল,0,"Meme, TikTok and others"
বাপ্পীর সব সিনেমা ফ্লপ,0,"Meme, TikTok and others"
আপু কেমন আছেন,0,"Meme, TikTok and others"
ওকে কঠিন শাস্তি দেওয়া হোক এবং এই বৃদ্ধ লোকটির দায়িত্ব সরকারের নেওয়া উচিত আর যদি ওকে কঠিন শাস্তি না দেওয়া হয় তাহলে জনগনের উচিত ওকে রাস্তায় জবাই দেওয়া,0,"Meme, TikTok and others"
আমার দনটাত ইনচি পারবেনি চুদা লইতে,0,"Meme, TikTok and others"
অকে ফাশি দিয়া হক,0,"Meme, TikTok and others"
আমি কাশমিরের সপখখের লোক মুধির মত কাপেরের সাথে নয়,0,"Meme, TikTok and others"
এসব মিথ্যাবাদী বিজেপির ষাঁড়েদের কথা বিশ্বাস কর নাআসামে নামে লক্ষ হিন্দু সম্প্রদায়ের মানুষ চরম নির্যাতিত হচ্ছে ডিন্টেনশন ক্যাম্পে বাংলায় হলে হিন্দু সম্প্রদায়ের মানুষেরা বেশি পস্তাবে,0,"Meme, TikTok and others"
এই দিনের অপেক্ষা করছিলাম আমি,0,"Meme, TikTok and others"
প্রতিবেশীদের আল্লাহ ভাল করুক,0,"Meme, TikTok and others"
বাপি তুমি টেরগাকেন,0,"Meme, TikTok and others"
আগে অপুকে আমি অনেক ভালোবাসতাম কিন্তু এখন অনেক অপছন্দ করিএকদিন আফছুছ করবিতখন কুনু কাজে আসবেনা,0,"Meme, TikTok and others"
ভদ্র বেসে সয়তান,0,"Meme, TikTok and others"
বাবামা এর সাথে,0,"Meme, TikTok and others"
তার পোশাক এ বুঝা যায় সে কেমন হতে পারে,0,"Meme, TikTok and others"
আমি একটা পাত্রী চাই আমি একটা পাত্রী চাই আমি বিয়ে করবো,0,"Meme, TikTok and others"
দেশের সব থেকে বড় শত্রু পৃথিবীর সবচেয়ে বড় আতঙ্ক বাদি মোদী ও অমিতশা এদের কে ফাঁসির থেকেও ভয়ঙ্কর মৃত্যু দণ্ড দেওয়া হোক,0,"Meme, TikTok and others"
কালকে বলবেন সবাই এর পা দরে বলছি কমেন্ট লাইক করন এরপর সবাই করবে আর আপনাকে বলতে হবে না বার বার,0,"Meme, TikTok and others"
এটা ভিডিও করলো কে,0,"Meme, TikTok and others"
চিনের প্রধান মন্রী ভারত সফর করছে শালি মিথ্যা খবর দিস কেন,0,"Meme, TikTok and others"
কাস্মির সাধিন চাই,0,"Meme, TikTok and others"
একজন মুসলমান বেচে থাকলেও মুদির আশা পুরন হতে দেেবনা,0,"Meme, TikTok and others"
আমার মনে হয় এরকম ছেলেকে আগুনে পুরিয়ে মারা দরকার,0,"Meme, TikTok and others"
আমি চাই একহয়ে জাক,0,"Meme, TikTok and others"
অমিতশাহাকেজুতামারি,0,"Meme, TikTok and others"
আমি চাই সাকিব ও আপু একসাথে থাকে এটা চাই,0,"Meme, TikTok and others"
আল্লাহ কাশ্মীরকে হেফাজত করুন,0,"Meme, TikTok and others"
ইৰান,0,"Meme, TikTok and others"
হিরো আলম বাপ্পীর চেয়ে অনেক বেশি ফেবারিট,0,"Meme, TikTok and others"
বিলে বিপক্ষে কারণ নিজের চাকরী নিজের জমি কেন বিদেশী হিন্দু বা অন্য জাতি দেবো দেবো তো জাতি ভেদাভেদ কেন দেবো যা ভারতীয় সংবিধানের আইন ভেঙে মানব হত্যা পাপ,0,"Meme, TikTok and others"
ওনার মেয়েকে আইন মতাবিক যত তাড়াতাড়ি সম্ভব তেজ্যকন্যা করা উচিৎ,0,"Meme, TikTok and others"
আমি সরাসরি কতা বলচি দিন আজও মনে পরে,0,"Meme, TikTok and others"
ঠিক বলেছেন আপনি,0,"Meme, TikTok and others"
আমাদেরমখ্যমন্তরীহিন্দিদেরকখনোভখলোচাইনা,0,"Meme, TikTok and others"
আমি তোমাকে গালি দিয়ে তোমার মতো হতে রাজি না,0,"Meme, TikTok and others"
একা একা হাসেন কেন দশক হাসে না শুধু আপনারা ই হাসেন,0,"Meme, TikTok and others"
ভিখারি ভিখারি থাকা উচিত কুকুরে পেটে ঘি সোজ্জো হয়ে,0,"Meme, TikTok and others"
আল্লাহ কি দেখায়লা ওর ফাঁশি চায়,0,"Meme, TikTok and others"
কত নিবা ভিডিও সেক্স,0,"Meme, TikTok and others"
পাকিস্তান এন্ড কাস্মীরীর পক্ষে,0,"Meme, TikTok and others"
আমরা মুসলমান আমাদের বাবরি মসজিদ চাই,0,"Meme, TikTok and others"
কুলাঙ্গার সন্তান,0,"Meme, TikTok and others"
শাকিব নাম্বার ওয়ান হিরো বাংলার,0,"Meme, TikTok and others"
মেরেফেল,0,"Meme, TikTok and others"
শয়তানের বাচ্চা,0,"Meme, TikTok and others"
পৃণিমার লজ্জ কম,0,"Meme, TikTok and others"
জাকির নায়েক,0,"Meme, TikTok and others"
এউ রায় বুল,0,"Meme, TikTok and others"
পাকিস্তান জিন্দা বাদ কাশ্মীর স্বাধীন চাই ভারত নিপাত যাক,0,"Meme, TikTok and others"
আপু আপনি সিনেমা ছেরে আল্লাহর দিনের পতে আস পরকালে পূন্যের জীবন গরি আমরা মুসলিম,0,"Meme, TikTok and others"
আফ্রিদি ঠিকই বলেছে বন্ধ করার দরকার এনআরসি বন্ধ করার দরকার,0,"Meme, TikTok and others"
মানুষ তো একটা সম্পর্ক করে আর আঁখি তো মেলামেশা করার জন্যে সম্পর্ক করে,0,"Meme, TikTok and others"
কেয়ামত খুব নিকটে,0,"Meme, TikTok and others"
কাশ্মীরীর পক্ষে,0,"Meme, TikTok and others"
আরে ভাই এটা আবার নতুন করে জানার কি আছে শত শত ভক্ত অপেক্ষা করে আছে শাকিব অপু জুটিকে দেখার জন্য সবসময় আর আমি তো শাকিব অপুর বিগ ফ্যান,0,"Meme, TikTok and others"
নো ইন্ডিয়া নো পাকিস্তান কাশমির আজাদী চাই,0,"Meme, TikTok and others"
আভাল,0,"Meme, TikTok and others"
নরেনদ্র মদি আমাদের প্রকাশ্য শত্রু,0,"Meme, TikTok and others"
আপনার আর আপনার পেরেমিকের গোপন ভিডিও ফাঁস করে দেবেন কবে যত সব ফাযলামি,0,"Meme, TikTok and others"
ছি এমন ছেলেকে জন্মাবার সময় মরে যাওয়া উচিৎ ছিল,0,"Meme, TikTok and others"
এই দাদুর সাথে আপনাকে বিয়ে দেয়া দরকার,0,"Meme, TikTok and others"
পাহাড় ধসে মরতে চাইনা,0,"Meme, TikTok and others"
সে ও কোন বাবার সন্তান আমরা ও তো একটা বাবারই সন্তান আজ বাবা নেই খুবই বেশী মনে পরছে বাবাকে,0,"Meme, TikTok and others"
বর্ডার এর পুলিস কি মশা মারে,0,"Meme, TikTok and others"
আল্লাহ মানুষের মনুষ্যত্ব এখন কোথায় _#,0,"Meme, TikTok and others"
মিথ্যা আশ্বাস বিশ্বাস করবেন না জাকির নায়েক প্রিয় জাকির নায়েক স্যার আপনার ফিরে যাওয়া ঠিক হবে না,0,"Meme, TikTok and others"
আজগুবি গল্প কই পান,0,"Meme, TikTok and others"
বাজে মহিলা পতিতার রাণী,0,"Meme, TikTok and others"
ধর্ম নিয়ে কথা বলিস না,0,"Meme, TikTok and others"
ফোরের জমি ধান কেয়া গরু ধান না খাই তাকতে পারে না মিথিলা হলেন ধান খাই গুরু ধান খাই তে গেছে,0,"Meme, TikTok and others"
বাবরি মছজিদ আছে এবং থাকবে এর জন্য এই বার মুছলিম জিবন দিছে দরকার হয় আবার জিবন আমি দিব আমিন মুদি তুমি হুশিয়ার তুমার খবর আছে পুলুমার কতা জানা আছে,0,"Meme, TikTok and others"
ভাই আমি চোখের পানি রাখতে পাচ্ছি না মানবতা হারিয়ে গেছে এই জন্য কি বাপমা ছেলেকে জন্ম দেয় যারা এর জন্য প্রতিবাদ করেছে তাদেরকে প্রবাস থেকে অনেক ধন্যবাদ,0,"Meme, TikTok and others"
এইটা নায়ক হল নাকি,0,"Meme, TikTok and others"
ভারত কত বড় একটা রাজ্য এর পরেও সাবাই কত সুন্দর বিচার পায় আরা আমাদে বাংলাদেশ কত উন্নত এর পরেও ন্যয় বিচার পায়না মানুষ এখান থেকে আমাদের শিক্ষা নেয়া উচিৎ,0,"Meme, TikTok and others"
লাক্স বিশ্বসুন্দরী,0,"Meme, TikTok and others"
সোহেল চৌধুরি মারা গেছেন কিন্তু অশ্লীল নায়ক হচ্ছেন সোহেল খাঁন,0,"Meme, TikTok and others"
মিন্নি খারাব আর মিথো বাদি,0,"Meme, TikTok and others"
এমরান খান তুম এগিয়ে যাওভারতের সাথে যুদ্ব ছারা বিকল্প নাই,0,"Meme, TikTok and others"
এমন সন্তানকে মাটিতে জীবিত পুঁতে ফেলা উচিত,0,"Meme, TikTok and others"
ভাই জাকির নায়েক তো ভাই নিজের দেশেই থাকতে পারেনা ওনি যদি এত ভাল মানুষই হয়ে থাকে তাহলে নিজের দেশ ছেড়ে অন্য তার কেন থাকতে হবে কেন ভাই ধমঁ প্রচার করা ভাল দিক কিন্তু অন্য কে ছোট করে নয় এটা একটু ভেবে দেখবেন সবাই ভাল থাকবেন,0,"Meme, TikTok and others"
মিন্নির কোন দুস নেই,0,"Meme, TikTok and others"
অনেরক অনেক ভালো লাগছে,0,"Meme, TikTok and others"
তাদের মধ্যে খুবই ভালো সম্পর্ক,0,"Meme, TikTok and others"
সচেতন বলে বলে মানুষকে নির্লজ্জতার শেষ প্রান্তে নিয়ে গেছে,0,"Meme, TikTok and others"
বোকাচোদা,0,"Meme, TikTok and others"
মিথিলা খারাপ,0,"Meme, TikTok and others"
ওকে পাথর মারতে মারপে পৃথিবী থেকে বিদায় করা হক,0,"Meme, TikTok and others"
গুড সাকিব,0,"Meme, TikTok and others"
আপু প্লিজ প্লিজ প্লিজ আমার চ্যানেলটি সাবস্ক্রাইব করুন,0,"Meme, TikTok and others"
সাকিব অপুর জুটি চাই,0,"Meme, TikTok and others"
কাশ্মীর সাধীন পাকিস্তান,0,"Meme, TikTok and others"
বাসায় কি একা সেক্স করতে মন চায় তুমি কি চাও কেউ এসে তোমার ভোদা চুষে দিয়ে যাক বিধবা বিপত্নিক তালাকপ্রাপ্ত গৃহিনী ছাত্রী আবিবাহিতা স্বামী বিদেশে বাচ্চা হয় না আপু ভাবী আন্টি তোমরা যারা সেক্স এর জ্বালায় ভূগছো সোনালী সময় নষ্ট না করে ফোন কর,0,"Meme, TikTok and others"
আমরার শেষ চাওয়া এর বিশ্ব কাপ,0,"Meme, TikTok and others"
ভালো মানুষ ন্যায়ের বিরুদ্ধে লড়েত পারে এবং ধার্মিক,0,"Meme, TikTok and others"
উরি বাব্বাইরান আর তুর্কিকি বিশাল শক্তিশালী দেশ রে বাওয়াআমরা তো সব ভয় পেয়ে গেছিশোন্ভারত কে সবার প্রয়োজনভারত এর কাও কে দরকার নেইআমরা একাই,0,"Meme, TikTok and others"
ওরে লাইফে এনে দিন তিন বেলা জুতা পিটা করতে হবে ওর ওই জায়গায়,0,"Meme, TikTok and others"
কী ফালতু নিউজ ছাড়ে,0,"Meme, TikTok and others"
বাবামারাএইচেলেকেমারা,0,"Meme, TikTok and others"
ধন্যবাদ প্রতিবেশীদের,0,"Meme, TikTok and others"
আপনী উনার প্রশংসিত কথা বলছেন কুকুরের লেজে ঘীমালিশ করলে সোজা হয়না অধীন করে অনেক ধ্যনবাদ আ জ এমন কথা,0,"Meme, TikTok and others"
কপালপোড়া,0,"Meme, TikTok and others"
ঠিক হোয়েছে সাকিব ভন্ড,0,"Meme, TikTok and others"
অপুকে মেনেনাও,0,"Meme, TikTok and others"
শাকিব খান রাজা অপু রানি তাদের ছেলে জয় রাজকুমার তাদের ফ্যামিলি কতটা সুন্দর হতো,0,"Meme, TikTok and others"
যথাযথ বিচার চাই তাকে এমন শাস্তি দেয়া হোক যেন আর কখনো না করে,0,"Meme, TikTok and others"
জুতার মালা গলাই দিয়ে বের করে দিয়া উচিত মেয়ের সেলফিশ একটা,0,"Meme, TikTok and others"
ক্যাপশনে খারাপ কথা বাট ভিডিওতে পারিশ্রমিকের কথা বলাদুনাম্বারী ক্যাপশনে লাইক টানার কৌশলমিথ্যাবাদী সব,0,"Meme, TikTok and others"
তোরা বালের খবর প্রচার করছিস পাকিস্তান তোদের বাংলাদেশ দখল করবে ভারত আছে বলে পারছে নাভারত তোদের মাথায় হাত রেখেছে বলে তোরা বেচে আছিস সরিয়ে নিলে তোরা মরে যাবি এর আগে যেমন ছিলি পাকিস্তান তোদের সেরকম করবে,0,"Meme, TikTok and others"
কাশ্মীর রে স্বাধীনতা চাই,0,"Meme, TikTok and others"
কাম্শীর স্বাধীন চাই,0,"Meme, TikTok and others"
সাকিব খানের উপর খোদার গজব পরুক,0,"Meme, TikTok and others"
আমিও তাদের তিনজনকে অনেক বেশি ভালোবাসি এবং কি সব সময় তাদেরকে খুব মিস নতুন নতুন যে ছবিগুলা আসেন সবগুলো ছবি আমি দেখি আবেগ অনুভব করি আন্তরিকভাবে আমার মন থেকে তাদের জন্য অনেক ভালোবাসা,0,"Meme, TikTok and others"
হিন্দু মুসলিমের ঐক্যবদ্ধ থাকা বসবাস জীবন কে আলাদা হওয়া চরম কৌশলআসেন আমারা ঐক্যবদ্ধ টিকিয়ে রাখতে চরম ভাবে এর বিরুদ্ধে প্রতিবাদ জানায়,0,"Meme, TikTok and others"
অাহ বুকের ভিতরে অাগাত লাগে যখন বৃদ্ধ বাবাকে মারে,0,"Meme, TikTok and others"
জয় আসাঊদ্দিন,0,"Meme, TikTok and others"
ওরে বাবা রে বাবা,0,"Meme, TikTok and others"
তোরা এর থেকে আর কি পারবি,0,"Meme, TikTok and others"
চাই চাই ফাঁশী চাই,0,"Meme, TikTok and others"
নৌবাহিনীর লোক পিছের টা রবোট নাকি,0,"Meme, TikTok and others"
শাকিবের উচিত অপু বিশ্বাসের সাথে মিলে যাওয়া না হলে বাচ্চাটার জীবন থেমে যাবে,0,"Meme, TikTok and others"
তার মানে ওর বাবাকে সব সময় ও মারে,0,"Meme, TikTok and others"
বস সাকিব খান আমারদের বস,0,"Meme, TikTok and others"
আগে বৌয়ের বিচার করা দরকার তারপরে ছেলেকে ফাশির দড়িতে ঝুলিয়ে মারা দরকার,0,"Meme, TikTok and others"
মোদি চা ওয়ালা দেশে প্রদান শান্তি দিতে পারে না নিজে সাতে মানুষ জাতি দংশ করিবে মোদিনিজে ছিলে খোদাত মানুষে কি বাবে খাবার দিবে শান্তিতে ভারত কোনু দিন শান্তি হবে না মানুষ জাতি হিসাবে সরকারী আই শক্ত না করিবে,0,"Meme, TikTok and others"
কুতার বাচ্ছা,0,"Meme, TikTok and others"
যেমন করবে তেমন পাবে উন্নতি আর অবনতি যেটা ভালো লাগে করবে,0,"Meme, TikTok and others"
গান ভালো লাগে,0,"Meme, TikTok and others"
বাংলাদেশে এসব হয় ছিঃ সমাজ কোথায় যাইতেছে,0,"Meme, TikTok and others"
হট মেয়েরা ইমুতে আসো,0,"Meme, TikTok and others"
ঘৃণ্য মোদী ও অমিত এত হিংসা বিদ্বেষ মুসলমানদের জন্য তাদের বীভৎস চেহারা দেখে বুঝা যাচ্ছে এত হীন মন্য হতে পারে কোন মন্ত্রী প্রধান মন্ত্রী একটি ধর্মীয় সংখ্যালঘু সম্প্রদায়ের প্রতি এর থেকে বুঝা যায় ঐ সম্প্রদায়ের লোকজন ভারতে কত নির্যাতন ও বৈষম্যমূলক আচরণের শিকার মানবতাবাদী ভারতীয়দের ধন্যবাদ মমতা ব্যানার্জিকে ধন্যবাদ যে তারা এই চক্রান্তের বিরুদ্ধে কঠিন লড়াইয়ে অবতীর্ণ হয়েছেন,0,"Meme, TikTok and others"
আমাদের মোজি ছাই,0,"Meme, TikTok and others"
জীবনের এক খারাপ মুহুর্ত দেখলাম,0,"Meme, TikTok and others"
আপু তোমার সাতে একটু কথা বলতে চাই কল দিবেন,0,"Meme, TikTok and others"
কেন ছরাস,0,"Meme, TikTok and others"
চল আলোর পথে চলিইসলামের পথে চলি,0,"Meme, TikTok and others"
শাকিব খানের খতি যারা করেন তারা সবাই একদিন হারিয়ে যাবে,0,"Meme, TikTok and others"
আমারা চাই সাকিব খান ও অপু বিশ্বাস এক হক দুজনের ছবি দেখতে চাই আমার সব ছবি ভালো লাগছে,0,"Meme, TikTok and others"
ছোট লোক যতই বড় হোক না কেন তার আদত ছোটলোকের ন্যায় থাকে,0,"Meme, TikTok and others"
সবাই বাপ্পিকে অনেক হেয়ো করে কথা বলছে কারনটা আমার জানা নেইতবে এটি বলতে পারি আমরা দেশকে কখনোই ভালবাসতেই পারি নাইবাপ্পি কি বলছে তার সমতুল্য কেউ নেই বা তার সাথে প্রতিদ্বন্দ্বীতা করার মত কেউ নেইসে শুধু বলছে আমি কাউকে প্রতিদ্বন্দ্বী মনে করি না আমরা আসলেই আজব বাংগালী,0,"Meme, TikTok and others"
ভালো করে বাংলা বলা শিখুন,0,"Meme, TikTok and others"
দোস্ত লাইভ ভিডিও কোথায় পাওয়া যায়,0,"Meme, TikTok and others"
বিচার চায় ভাই,0,"Meme, TikTok and others"
এই ছেলের বিচার চাই কঠিন,0,"Meme, TikTok and others"
আমি তকে সরাসরি খেলতে পারবো যদি হয় যত টাকা লাগে আমি দিবো কারন তকে আমার ভালো লেগেছে,0,"Meme, TikTok and others"
আল্লাহ অরে তুমি উঠেয়ে নেও,0,"Meme, TikTok and others"
তুই জাহান নামে জাবি,0,"Meme, TikTok and others"
নানা আপনি কোথায় আচেন আমি আপনার পাশে থাকবো,0,"Meme, TikTok and others"
সাকিব বেরে জুতা মারো,0,"Meme, TikTok and others"
অনেক ভাল লাগলো,0,"Meme, TikTok and others"
সাবাস সবাই কে,0,"Meme, TikTok and others"
অপু আপা অনেক ভালো,0,"Meme, TikTok and others"
অনেক দিন পরে দেখলাম মুয়ুরী আপুকেসেই ছোট বেলায় তার অনেক ছবি দেখেছিমুয়ুরী আপুকে দেখে ছোট বেলার কথা মনে পড়ে গেল আপু চুলটা কালার না করলে আর বেশু ভাল লাগত,0,"Meme, TikTok and others"
এত ভুল বললে হবে কি করে,0,"Meme, TikTok and others"
টিইমার হয়েছে #,0,"Meme, TikTok and others"
পাগলি,0,"Meme, TikTok and others"
সবাই চাই শাকিব বহিষ্কার হোকতা না হলে হল বন্ধ হয়ে যাবে,0,"Meme, TikTok and others"
সবার কমেন্ট পরে একা একা অনেক হাসলাম,0,"Meme, TikTok and others"
নামাজ নিয়ে একি বললি তুই তোকে আল্লাহ ক্ষমা করবেনা,0,"Meme, TikTok and others"
আমার সামনে হলে শালার পুত গলা কাটতাম,0,"Meme, TikTok and others"
প্রতিবেশীদের প্রণাম জানাই,0,"Meme, TikTok and others"
শাকিব খান অপু বিশ্বাসের সাথে বেইমানি করলে ঠিক হবে না অপু বিশ্বাস হিন্দু ধর্ম ত্যাগ করে মুসলিম গ্রহণ করেছেন তাকে যদি থাকে জাতির বেইমান হবেন,0,"Meme, TikTok and others"
গুখা কুলাঙ্গার সয়তান,0,"Meme, TikTok and others"
আমি এই চ্যানেলটি করে বেরিয়ে গেলাম,0,"Meme, TikTok and others"
হে তারা যেন মিলে র‍্যায় শাকিবকে যেন হেদাত করে,0,"Meme, TikTok and others"
না না ওকে আপনাকে অনেক অনেক ধন্যবাদ নিউজ শোনানোর জন্য বাই,0,"Meme, TikTok and others"
সামনে পেলে শয়তানটাকে ঝাটা জুতা দিয়ে পেটাতাম,0,"Meme, TikTok and others"
আপু আপনার দুধ দুইটার অবস্থা খারাপ মিষ্টি কুমড়ার মত বড় বড়,0,"Meme, TikTok and others"
লড়াই তকবির আল্লাহু আকবর,0,"Meme, TikTok and others"
বুলির দূধ টিপে বরকরছে শাকিব,0,"Meme, TikTok and others"
এরপরে তার বাবা বলসে আমি তো কাউকে বলি নি আপনারা কিভাবে জানলেন এমন বাবাকে কিভাবে মারে,0,"Meme, TikTok and others"
ওর ফাসি চাই,0,"Meme, TikTok and others"
ভারত থাকতে চাই আমরা,0,"Meme, TikTok and others"
একদাম ঠিক,0,"Meme, TikTok and others"
যারা সিনেমা করে তাদের আবার জাত আছে,0,"Meme, TikTok and others"
ভাই আমি কিজে বলবো আমার কোন ভাষা নাই,0,"Meme, TikTok and others"
বাপ্পির অভিনয়‌ হাসসোকর পাবলীগ দেখে চে্নেল চেন্জ করে দেয়,0,"Meme, TikTok and others"
ব্যাদব,0,"Meme, TikTok and others"
দে বাশঁ আইক্কাওয়ালাশালি ইহুদি বলে কিআরাম আছেতো কার সোনার চাপ খেয়ে আবুল তাবুল বলছে,0,"Meme, TikTok and others"
কাশ্মির হলো বাংলার জনগনের প্রানস্পন্দন,0,"Meme, TikTok and others"
ওর অনেক জনের তা না নিলে ভাল্লাগেনা,0,"Meme, TikTok and others"
ভালোই লাগল,0,"Meme, TikTok and others"
টাকলুকে গুরা মরিচ দিয়ে পাচা মারবো,0,"Meme, TikTok and others"
জয় অনেক সুন্দর দেখলে মন ভরে যায়,0,"Meme, TikTok and others"
সেই গাল,0,"Meme, TikTok and others"
আমি এই ছেলের ফাঁসি চাই,0,"Meme, TikTok and others"
মসজিদ চাই চাই চাই চাই,0,"Meme, TikTok and others"
শাকিব খান কিংখান,0,"Meme, TikTok and others"
জেম নেরোম কি কারণে আমাকে পাগল বলছেন আমি তো আপনাকে অসম্মান করিনি তাহলে আমাকে অসম্মান করলেন কেন,0,"Meme, TikTok and others"
সাকিব ভাইয়ে সাথে আমি এক মত,0,"Meme, TikTok and others"
কাশ্মীরে মাবোনদের বেইজ্জতি করলো সেনারা,0,"Meme, TikTok and others"
নাই,0,"Meme, TikTok and others"
ইয়া আল্লাহ কোলকাতায় এসব কি হয় ছিঃ ছিঃ ছিঃএমন ছেলেকে ফাসি দেওয়া উচিত,0,"Meme, TikTok and others"
সোহেল চোধুরী খুন হয়েছেন অনেক আগেই মৃত মানুষকে নিয়ে মিথ্যা খবর ছড়ানো অফ করুন,0,"Meme, TikTok and others"
আছাউদিকেছালামওকেকথা,0,"Meme, TikTok and others"
এ দেশে বিচারের আশা করিনাকার দোষ কি দোষ জাইনা কোনো লাভ নাইদিন পর এই মামলার কোনো খবরই থাকবেনা,0,"Meme, TikTok and others"
সুলতানা বিবিয়ানা এপার ওপারদারূন মুভী বস্,0,"Meme, TikTok and others"
খুব সুনদর,0,"Meme, TikTok and others"
সর্বোচ্চ শাস্তি দেওয়া দরকার,0,"Meme, TikTok and others"
মৌসুমি আপু ঠিক বলছে,0,"Meme, TikTok and others"
ইনি কি বাংলাদেশের রাষ্ট্রপতি,0,"Meme, TikTok and others"
তাহসান ভাই একজন ভালো মানুষ তাকে আমি সম্মান করি আর মিথিলার জিবনে কস্ট আছে,0,"Meme, TikTok and others"
শালিন আর অশালিন বলে দুটো কথা আছে আমি জানতে চাই তোমার পোশাক টা কি শালিন না অশালীন,0,"Meme, TikTok and others"
ওকে পাসি চাই,0,"Meme, TikTok and others"
কুকুর বাচ্চা,0,"Meme, TikTok and others"
আল্লাহর ভয় নেই হায়রে সভ্যতা,0,"Meme, TikTok and others"
একে এমন সাস্তি দেওয়া হোক পরে যেনো আর কাউকে না করতে পারে,0,"Meme, TikTok and others"
সাকিব অপুকে ভাললাগছআমরা ওদের ভিডিও চাইসাকিব অপুর মুবি চাই ওদের খুব ভাল লাগে,0,"Meme, TikTok and others"
করতে চাই কোথায় আসতে হবে বল,0,"Meme, TikTok and others"
হিন্দুস্তান বাংলাদেশের অতীতেও শত্রু ছিল এখনও শত্রু আছে এবং ভবিষ্যতেও বালিশের শত্রুই থাকবে কারণ হিন্দুস্থান কখনো বাংলাদেশের ভালো চাইনি কিন্তু দুঃখজনক হলেও এটা সত্য যে বাংলাদেশের মধ্যে কিছু কুলাঙ্গার আছে এক নাম্বার কুলাঙ্গার দল হচ্ছে আওয়ামী লীগ এবং দ্বিতীয় কুলাঙ্গার হচ্ছে আওয়ামী লীগের সহযোগী সংগঠন আওয়ামী লীগের সাথে যেসব জোটবদ্ধ হয়ে আছে সেসব কুলাঙ্গারদের জন্য আজ বাংলাদেশ বিপর্যস্থ,0,"Meme, TikTok and others"
অপকে মেনে না নিলে সাকিবের কোনো ছবি দেখবোনা,0,"Meme, TikTok and others"
বাঙলা দেশে ম্যাঁয়া কমে গেলো নাকি মিয়া সাহেব নিজের মায়া টারে বিয়া কৈরা নিলেই তো পারেন ওটা তো ইছলামে জায়েজ আছে,0,"Meme, TikTok and others"
শাকিবের কথা শুনলেমন চায় আগে জুতা খুলি,0,"Meme, TikTok and others"
ছাগল,0,"Meme, TikTok and others"
আরে শাকিব তুই কতটা বিবেকহীন হলে বলতে পারিস অপু সিনেমা ছেড়ে দিতে তুই কি ভেবেছিস কোনো সাধারন মেয়ে তোর সংসার করবে তুই থাকবি সিনেমা জগতে নাচবি গাইবি শুইবি বসবি জরিয়ে ধরবি বিভিন্ন নায়িকাদের আর ঐ সাধারন মেয়ে সেগুলো মেনে নিবেঅপু মিডিয়া জগতের বলেই তুর এত অত্যাচার লুচ্চামি সব মথা পেতে নিয়েছে,0,"Meme, TikTok and others"
আপডেট পেতে চ্যানেল সাবস্ক্রাইব করবেন,0,"Meme, TikTok and others"
ভাইয়ারা ওকে পিটাদেন,0,"Meme, TikTok and others"
মুসলিম ছাড়া সমস্ত ধরমের লোক জাহান্নামে নিখ্যেব করবেলাল টিপ দিয়ে খ্যরের ভুতির পুজা করে লাভ নাই মসজিদে নামাজ পড় জান্নাত নিশ্চৎ,0,"Meme, TikTok and others"
ভাই তোমরা শুধু ছবি দেখে ভিডিও বানানো বন্ধ করো ভিডিও যদি থাকে সেটা দেখাও,0,"Meme, TikTok and others"
আমার বাড়ি বগুড়া তোমাকে ভাল লাগে তোমার ইমু নামবার দিবা আমার নামবার সাবাই লেখতে পারে কিন্তু তুমি আমাকে মিস কর#,0,"Meme, TikTok and others"
রবীন্দ্রনাথের একটা কথা আছে,0,"Meme, TikTok and others"
এটা সবার ই জানা,0,"Meme, TikTok and others"
জাকির নায়েক মালয়েশিয়ার জন্য মোটেও হুম কিনা বরং কাফেরেরা ইসলামের হুম কি,0,"Meme, TikTok and others"
পার্সওয়াডের বাজেট বেশী হলেও শাহেন শাহ সাথে যাইতে পারবে না,0,"Meme, TikTok and others"
অপু কে মেনে নাও,0,"Meme, TikTok and others"
ফাসি চাই এরকম ছেলের জন্য সমাজের ছেলেরা খারাপ হয়ে যাবে,0,"Meme, TikTok and others"
আর না এখন হর হর মোদি,0,"Meme, TikTok and others"
সে তো একজন নিরিহ বাবা মিডিয়া প্রশাসন যা করল তা আপেক্ষিক দৃষ্টিতে ভালো কিন্তু ঐ বাবার জন্য কি এটা স্থায়ী সমাধান সমস্যা কি অগের থেকে বাড়বে না কমবে ঐ ছেলে ছাড়া পেলে তার বাবার সাথে সদয় হবে না হয়তো আরো বিরূপ আচরনই করবে কোনো স্থায়ী সমাধান করলে ভালো হত,0,"Meme, TikTok and others"
এই ছেলেকে পুলিশ এর হাত এ দেওয়া উঠিত আমার সাথে কে কে একমত,0,"Meme, TikTok and others"
অপু কে আমার বালো লাগে অপুর সব বালো লাগে তার দুধ গুলা বেশি বালো লাগে,0,"Meme, TikTok and others"
মুসলমানদের সাথে আছি,0,"Meme, TikTok and others"
তুমি নারী জাতির কলংক,0,"Meme, TikTok and others"
কশ্মীর,0,"Meme, TikTok and others"
এই বালকের বাবা মা ভারতের স্পাই কিনা দেখা উচিত,0,"Meme, TikTok and others"
শাকিব খান অপু বিশ্বাস শাকিব খান সব ভেদাভেদ ভুলে অপু বিশ্বাস ছবি করুক সেট করব দর্শকরা,0,"Meme, TikTok and others"
হাত কেটে দেওয়া উচিত,0,"Meme, TikTok and others"
চোখে পানি চলে আসল,0,"Meme, TikTok and others"
তুই একটা টা বাংলাদেশী এই ভাবে মানুষকে কি দরকার তুই তাল খাওয়া বাংলাদেশী,0,"Meme, TikTok and others"
আজ বিল নিয়ে পৃথিবীর বিভিন্ন রাষ্ট্র মুসলিম দের পক্ষে সরব হয়েছে এমন কি পাশের রাষ্ট্র বাংলাদেশ ও ম্যাডাম হাসিনা ও ভারতের বিপক্ষে নানা বিরূপ মন্তব্য করেছেন করছেন কিন্তু সবার কাছে একটি প্রশ্ন যখন পূর্ব পাকিস্তান বা বর্তমান বাংলাদেশ ও পশ্চিম পাকিস্তানআফগানিস্তান থেকে অ মুসলিম বিশেষ করে হিন্দুদের অত্যাচার করে খুন করে তাদের বাড়ীর মহিলাদের ধর্ষণ করে খুন করে হিন্দুদের ঘর বাড়ী জমি জায়গা দখল করে নিয়ে তাদের জন্ম ভিটে থেকে উচ্ছেদ করে সর্বস্ব কেড়ে নিয়ে তাদের কে নিঃস্ব করে পালিয়ে যেতে বাধ্য করেছিল মুসলিম রা তখন এই মুসলিম ভক্ত রা বা এই রাষ্ট্ প্রধানরা ও ম্যাডাম হাসিনা কোথায় ছিলেনএমন কি আজ উনি যে রাষ্ট্রের প্রধানমন্ত্রী হয়ে খেয়ে পড়ে বেঁচে আছেন সেটাও তো এই ভারতের দান যা পাকিস্তানের কাছ থেকে কেড়ে ওদের গিফট করে তানাহলে আজও ওনাকে এবং ওনার পরিবারের সদস্যদের এত লাক্সারি বিদেশে বসবাস ধন সম্পত্তি কোথায় পেতেনএখনো ওনাকে ও ওনার দেশের মানুষদের ওই পাকিস্তানের গোলামী করতে হতো এবং হীনও মার্সিডিজ বিভিন্ন গাড়ী চাপা বেরিয়ে যেতো সব পাকিস্তানে চলে যেতঅবশ্য এরা বেশির ভাগই বেইমান এদের যে বা যারা ভালো বেসে পাশে বসায় তাকে বা তাদের ওরা গলা কেটে তার প্রতিদান দেয় এটাই ওদের বেশির ভাগ মানুষের চরিত্রে আছে এই বেইমানি র ফলে আজ গোটা বিশ্ব ভুগছে কবেজে এদের শুভ বুদ্ধি হবে তা ঈশ্বর জানেন,0,"Meme, TikTok and others"
আপনারা যদি মানুষ হন তাহলে এই মহিলাকে আর নিবেন কোন গানের মঞ্চে কোন জায়গায় প্রোগ্রাম এ নিবেন না,0,"Meme, TikTok and others"
বাংলার বীর,0,"Meme, TikTok and others"
এই রায়ের মাধ্যমে ভারতের হিন্দুত্ববাদের একক প্রকাশ পেয়েছে আল্লাহর পাকের ঘর আল্লাহ পাক রক্ষা করবেন ইনশাআল্লাহ,0,"Meme, TikTok and others"
আমার স্তন্ অনেক টাই বড় আছে আর কি বড় করব,0,"Meme, TikTok and others"
দেখি,0,"Meme, TikTok and others"
মানুষ জে জাতেরেই হোক মা বাবাতো মা বাবাই তাদের তুলোনা কারো সাথে হয়না ওতো একটা জানোয়ার,0,"Meme, TikTok and others"
ইন্ডিয়ার ধোন চুষবি,0,"Meme, TikTok and others"
আর বেশি দেরি নয় মোদি ফেরাউন মতো বিচার হবে আল্লাহর দুনিয়া কোন নরপশু ক্ষমতার বড়াই করে আল্লাহর গজব থেকে রেহাই পায়নি,0,"Meme, TikTok and others"
বিষয়টা অনেক দুঃখ জনক তাও বলি যে ব্যক্তি এই ভিডিওটা করছো #,0,"Meme, TikTok and others"
হিন্দুদের কাছে এরচেয়ে বেবি আর কি আশা করা জায়,0,"Meme, TikTok and others"
মুদির বাপের দেশ নয়,0,"Meme, TikTok and others"
ভারোত পাকিস্তান বুজিনা কাসমির সাধিন চাই,0,"Meme, TikTok and others"
বাবরি মসজিদের জন্য আপনারা সবাই এক হয়ে আন্দুল করুমআমি দেখেচি বর্তমানে সনাতন ধর্মের কিচু মানুষও এই মসজিদ না ভাঙ্গার জন্য প্রতিক্রিয়া জানিয়েছেন আদালত পক্ষ পাতিত্ব রায় দিয়েছে এই রায় কেউ মানবে না বাংলাদেশ থেকে,0,"Meme, TikTok and others"
এই নাম্বারে যোগা যোগ করেন,0,"Meme, TikTok and others"
ছেলের পাকা বাড়ি আর মায়ের জায়গা ওই ঝুপড়ি সদ্যোজাত অবস্থায় ওই ছেলের মুখে বিষ গুলে খাইয়ে দেওয়া উচিত,0,"Meme, TikTok and others"
ছেলে ও ছেলের বউ টা কে সাস্তি দিতে হবে,0,"Meme, TikTok and others"
গুজঁনক্ল,0,"Meme, TikTok and others"
সারা রাত কত,0,"Meme, TikTok and others"
ডাং জাকির নায়েকে কোনো দোষ নেই,0,"Meme, TikTok and others"
মন টা খারাপ হইয়া গেল,0,"Meme, TikTok and others"
আর বাংলাদেশের ফিগার কেমন,0,"Meme, TikTok and others"
রানুদির,0,"Meme, TikTok and others"
আমি এটা বিশ্বাস করিনা যে রাম মন্দির ভেঙে বাবরী মসজিদ নির্মাণ করা হয়েছে কারণ আমাদের ধর্মীয় গ্রন্থে আছে যে কোনো মন্দির ভেঙে মসজিদ তৈরি করলে সেই মসজিদে নামাজ হবে না,0,"Meme, TikTok and others"
সাকিব এর সাথে একমত সানাই মেয়ে হবার যোগ্য নয়,0,"Meme, TikTok and others"
অপু ভালো এ কথা বলে ছোট করবেনা,0,"Meme, TikTok and others"
মালএসিয়া,0,"Meme, TikTok and others"
সব ভুল খবর,0,"Meme, TikTok and others"
তুই মরে যা,0,"Meme, TikTok and others"
শাকিব অপু মিল হলে খুশি হবো,0,"Meme, TikTok and others"
কমেন্ট দেখলে মাথা নষ্ট হয়ে যাই,0,"Meme, TikTok and others"
তোমাকে আমরা অনেক পছন্দ করি প্লিজ তুমি অপু আপুকে মেনে নাও শুধু তোমার আব্রাহামের জন্য আর ক্ষমাশীল কে তো আল্লাহ ও পছন্দ করে,0,"Meme, TikTok and others"
বউ কি এভাবে মারতে পারে,0,"Meme, TikTok and others"
যে ধমা্বলম্ভি রা একটি শৈচাগরকে পুজা করে তারাত ইংরাজ দেরইন্দন গ্রহন করবেইত অন্য দিকে গাজওয়া তুলহিন্দের সময় অতি নিকট তাইত ভারতীয় শয়তানরা জালিমি আরম্ভ করছে,0,"Meme, TikTok and others"
সাকিব খানের সাথে আমি ও একমত,0,"Meme, TikTok and others"
নবভিজ্ঞজি,0,"Meme, TikTok and others"
কুওা বাচ্চা,0,"Meme, TikTok and others"
সব মিথ্যা খবর ইংরাজিতে মালেয়েশিয়াতে যে খবর ছাপানো হয়েছে সেখানে জাকির নায়েক কে না রখার ব্যাপারে কিছুই লেখা হয়নি এই মিথ্যা খবরটা বলার জন্যা চেলেনলটা সাস্ক্রাইব করতে পারলাম না,0,"Meme, TikTok and others"
কিভাবে কতা বলব,0,"Meme, TikTok and others"
সময় টিভির কাছে অনুরোধ রইলো এই পশু টাকে পুলিশের কাছে ধরিয়ে দিন এবং ওই অমানুষের সবোর্চ্চ শাস্তি নিশ্চিত করুনযাতে করে ভবিষ্যতে কেও এই রকম করার আগে অন্ততপক্ষে বার ভাবে,0,"Meme, TikTok and others"
রানুর মেয়ে একটা লুভি,0,"Meme, TikTok and others"
সাকিব অপু চাই,0,"Meme, TikTok and others"
তার না হয় মাথর ঠিক নেই উল্টা পাল্টা বলছে আমাদের তো মাথা ঠিক আছে আমরা কেন উল্টা পাল্টা বলবো যদের খারাপ কথা বলেছে তাঁরা বুঝতে পেরেছে তিনি কি বলতে চেয়েছিল ভুলে কি বলেছেতাই তো আরো সুযোগ দিয়েছে ‌ ইনকাম করতে ভিডিও বানিয়ে এরা কখনো বলে এ ভালো আবার বলে খারাপ আমার তালে তাল মেলাই,0,"Meme, TikTok and others"
মদির বিপক্ষে,0,"Meme, TikTok and others"
জাকির নায়েক আলার এক নিয়া মত,0,"Meme, TikTok and others"
খবর পাঠিকা চৈতালি আপনি সাফিয়ার মতো রোবট মনে হয় কারন আপনার এক পোশাকে ও এক ভঙ্গিতে সব খবর পরেন এটাই প্রমান করে ভরতিয় রোবট বেকার মানুষ আছে খবর পড়ার জন্যপ্রয়জনে বিজ্ঞাপন দিন,0,"Meme, TikTok and others"
অতিদো দাদা আপনে অনেক ভালো কাজ করেছ ছেনরানুদিকে খমা করে দিন আমি এক মুসলীম বোন আমার বাড়ি বাংলাদেশে,0,"Meme, TikTok and others"
আল্লাহ এই বেয়াদব সন্তানকে তুমি গজব দিয়ে ধংস করে দাও,0,"Meme, TikTok and others"
তুমি মুসলিমদের কলঙ্ক খবর পরার সময় জাকেটের চেন খোলা কেন যদি দেখানো উদেশ হয তাহলে পুরোটাই খুলে দিতে হয,0,"Meme, TikTok and others"
তোর গাল এতো খারাপ তুই মুহাম্মদ কে নিয়ে বাজে কথা কস কিল্লাই,0,"Meme, TikTok and others"
মাদারী,0,"Meme, TikTok and others"
একস,0,"Meme, TikTok and others"
যারা তাহসানকে ভালো বাসেন তারা লাইক দিবে,0,"Meme, TikTok and others"
মজ্জীদ আল্লাহ গর আল্লাহ গর হরাবার ক্ষমতা কারো নাই,0,"Meme, TikTok and others"
ভারতকে শায়েস্তা করার জন্য পাকিস্তানের পক্ষে,0,"Meme, TikTok and others"
অতীন্দ্র দা খুব ভালো মানুষ,0,"Meme, TikTok and others"
আপনি রাষ্ট্রপতি কম কমেডিয়ান বেশি মনে হচ্ছে একজন সুপ্রতিষ্ঠিত নারী কি করবে সেটা তার ব্যাক্তিগত বিষয় সেই নারী এতটাই ভদ্র যে সে আপনার বিপক্ষে কেস করেনি আন্তর্জাতিক মহলে,0,"Meme, TikTok and others"
অবস তাদেখে,0,"Meme, TikTok and others"
আল্লাহ তুমি এইরকম ছেলে আর কারো ঘরে দিও না এত খারাপ লাগতেছে চোখের পানি ধরে রাখতে পারতেছি নাআল্লাহ তুমি ওকে এত শাস্তি দিও যাতে দুনিয়ার মানুষ দেখতে পারে তুমি ওকে তিলে তিলে মারবা,0,"Meme, TikTok and others"
অাপনে খোতাই তাখোন,0,"Meme, TikTok and others"
শাকিব অপু কে এক সাথে ছবিতে দেখতে চাই,0,"Meme, TikTok and others"
আমাদের দেশ টার বিতরে কি সুরু হয়ে গেলো জানিনা সামনে আরো কি হয়ে,0,"Meme, TikTok and others"
আল্লা তুমি সিফাত উল্লাহ কে হেদায়াত দান করুন সবাই বলুন আমিন,0,"Meme, TikTok and others"
সটিক বলেছেন পপি,0,"Meme, TikTok and others"
ভারতীয় প্রশাসনের উপর শ্রদ্ধা জানাচ্ছি ব্যবস্থা নেয়ায়,0,"Meme, TikTok and others"
আমরা কাশ্মীর দের পক্ষে পাকিস্তান নারে তাকবীর আল্লাহু আকবার,0,"Meme, TikTok and others"
ইনি হল একজন ইসলাম বিরুদী মোদ খোর পাগল,0,"Meme, TikTok and others"
মুল কথা হলো ঈশ্বর প্রদত্ব যেটা আছে সেটাই ভালোযেমন আছেন তেমনি ভালো এর বাহিরে কোনটাই ভালো না,0,"Meme, TikTok and others"
তৎকালীন বাংলা চলচিত্রের সবচেয়ে ভদ্র শভ্য পর্দাশীল নায়িকা,0,"Meme, TikTok and others"
নায়কা শাহানাজ কোথায় আছে,0,"Meme, TikTok and others"
ভারতে হামলা করার মত শক্তি আমেরিকার ও নেই ফালতু খবর,0,"Meme, TikTok and others"
আমি সৌদি থেকে বলছি ও নাকে আইনের শাস্তি দেওয়া হক,0,"Meme, TikTok and others"
আল্লাহ তুমি রক্ষাকরো,0,"Meme, TikTok and others"
মুদির ফাসি চাই,0,"Meme, TikTok and others"
নামাজনিয়ে বকছকেনরে,0,"Meme, TikTok and others"
সভাব ঠিকতো সব ঠিক,0,"Meme, TikTok and others"
দেখতে ঘিন্না,0,"Meme, TikTok and others"
সাকিব খান ভাইয়া সাথে একমত আর তাকে বাংলাদেশ থেকে ভেরকরে দেওয়া উচিত একটা মেনামের কলংকো,0,"Meme, TikTok and others"
জানোয়ার থেকে ও অধম,0,"Meme, TikTok and others"
জাহান্নম তার কপালে,0,"Meme, TikTok and others"
তুমি কি জানো আমি ওকে বললাম চল টিভি দেখতে দেখতে সে কথা আমি আশিক,0,"Meme, TikTok and others"
রানু মন্ডলকে কেউ কি ঘ্রিনা করেন লাইক দিয়ে যান,0,"Meme, TikTok and others"
আমার চোখ দিয়ে পানি পড়ছে,0,"Meme, TikTok and others"
আমার ইমো নাম্বার,0,"Meme, TikTok and others"
আপনার এখন সময় আছে ঠিক হয়ে যান,0,"Meme, TikTok and others"
আরব দুনিয়ার মেয় দের কাছে এরা চুল ও নয় তার সুনদরি পতিযোগিতাই যা ই না বলে তাই,0,"Meme, TikTok and others"
সানাই ফেইল করবে এর সামনে,0,"Meme, TikTok and others"
জাকির নায়েক সবচাইতে ভালো মানুষ,0,"Meme, TikTok and others"
দুধ মাঙ্গগে খির দেঙ্গে কাশমির মাঙ্গগে চির দেঙ্গগেজয় মোদি জয় ভারতপাকিস্তান মুরদা বাত বাংলাদেশ সরকার ভারতের পিছনে আছে হা হা হা,0,"Meme, TikTok and others"
বলার মতো কোন ভাষা ফেলাম না,0,"Meme, TikTok and others"
অল্প পানির মাছ বেশি পানিতে গেলে ছপর ছপর করে,0,"Meme, TikTok and others"
সাকিব এইটাটিকনা,0,"Meme, TikTok and others"
গাধা কখনো ঘোরা হয় না আর রানুদি যতই মুম্বইয়ে যাক কেন তার কথা কখনো পাল্টাবে না,0,"Meme, TikTok and others"
হায়রে পুড়া কপাল ফুলের কলিটি মেলতেই ঝরে গেল উফ উফ,0,"Meme, TikTok and others"
বীর ছবিতে,0,"Meme, TikTok and others"
তোর চ্যানেল বন্ধ হয়ে যায় এবং লাইক না করে কেউ যদি তাহলে আমি খুব হ্যাপি হবো কি ফটো লাগিয়ে ছিস বে,0,"Meme, TikTok and others"
পাকিস্তানএর জন্য দোয়া রইলো,0,"Meme, TikTok and others"
মানুশ কত বোকা হয় এই প্রথম দেকলাম বলতাসি মিন্নি মুল আসামি,0,"Meme, TikTok and others"
নাস্তিক আল্লাহ তর বিচার করবে,0,"Meme, TikTok and others"
দুক্ষোজনক,0,"Meme, TikTok and others"
তুমারে ফাই লই অওও বাংলাদেশ,0,"Meme, TikTok and others"
এ মানুষ,0,"Meme, TikTok and others"
আল্লাহ এমন সন্তান কারো ভাগ্য দিয়েন না,0,"Meme, TikTok and others"
বগার ভিডিও বানাওনি এই সব ক্যাপশন দেও একটা আর ভিডিও আরেকক টা,0,"Meme, TikTok and others"
রানুর মেয়ে লোভী,0,"Meme, TikTok and others"
এই নিউজ টি শুদু মুসলিম রাই সমওন করবে কারন এরা জিনিষ টি তদনত করেনা যে কোন মিডিয়া কি বলছে আমি বুঝতে হবে শুদু জিনদাবাদ বলা উচিত নয,0,"Meme, TikTok and others"
এটা দেখে আমি কথা বলার ভাষা হারিয়ে ফেলেছি,0,"Meme, TikTok and others"
তোর ফাসি চায় তুই একটা পুসু,0,"Meme, TikTok and others"
আমি তুমাকে ভালোবাসি,0,"Meme, TikTok and others"
তোমাকে আমার সাসরি বানাবো,0,"Meme, TikTok and others"
আর কোন খবর নাই,0,"Meme, TikTok and others"
ওহ৷,0,"Meme, TikTok and others"
বহ জন তো গান শুনেছেন এক দুই করে টাকা ও দিয়েছেন কেউ তো দাঁড়িয়ে থেকে গান শুনে ছবি তুলে ভাইরাল করার প্রয়োজন মনে করেন নি তো যিনি করলেন তিনাকে এত লাঞ্ছিত হতে হচ্ছে ছি একী সমাজ ব্যবস্থা তবুও অতীন্দ্র জীবনে বড়ো হবে ঈশ্বরের আশীর্বাদ পাবে,0,"Meme, TikTok and others"
তোমা কে চাই,0,"Meme, TikTok and others"
ওর শাস্তি দেখে যেন আর কেউ বাবাকে পেটানো সাহস না দেখায়,0,"Meme, TikTok and others"
সব থেকে বেশি চাই বাবা মা এক সাথে থাকুক,0,"Meme, TikTok and others"
আমরা মশজিদ চাই,0,"Meme, TikTok and others"
এসব গাই মার্কা নায়কারা ভাল করেকথাও বলতে পারে না,0,"Meme, TikTok and others"
ওই ছেলের বউ আরো বেশি শয়তান ওই শয়তান কে পিটানো দরকার,0,"Meme, TikTok and others"
মরতে হব না,0,"Meme, TikTok and others"
উনি এতো দিন ডেনমার্কের ডানো দুধের কারখানায় ছিলো এখন এটা জানাতে এসেছেন,0,"Meme, TikTok and others"
ইন সাআললাহ বাংলাদেশ জিবো,0,"Meme, TikTok and others"
ওকে গেফতার করার জন্য আন্তরিক ভাবে জানানো যাচছে,0,"Meme, TikTok and others"
আমি সার্কাসে দেখছিলাম,0,"Meme, TikTok and others"
আমি কারপহে অবশই৷ পাকিস্তান জইহক,0,"Meme, TikTok and others"
আপনি জেনারেল শিক্ষা যত বেশিই দেন না কেন সত্তিকারের মানুষ হওয়ার জন্য ইসলামিক শিক্ষা জরুরী জরুরী জরুরী,0,"Meme, TikTok and others"
এই ছাগল তোদের শিরোনামের সাথে খবর সংবাদের মিল নাই কেন ছাগল তোরা কি মানুষ,0,"Meme, TikTok and others"
ওই রকম ছেলেকে জুতা মারা উচিত,0,"Meme, TikTok and others"
এগুলো মানুষ না মানুষ নামের জানোয়ার,0,"Meme, TikTok and others"
ছিঃ ছিঃ ছিঃ ছিঃ হাজার ছিঃএটা মানুষ ভাবতেও অবাক লাগে,0,"Meme, TikTok and others"
এটা যদি বাংলাদেশে হতো তবে একে প্রথমে পিটিয়ে আধমরা করতামপরে পুলিশে দিতামএদের মতো কুলাঙ্গার যেনো আল্লাহ শত্রুকেও না দেন,0,"Meme, TikTok and others"
তাহছান ভাই কত ভালো মানুষ,0,"Meme, TikTok and others"
তোর মত নৃকৃষ্ট সন্তান যেন কারো না হয়,0,"Meme, TikTok and others"
রাজবাড়ী ইত্যাদি,0,"Meme, TikTok and others"
বীর পুরুষ,0,"Meme, TikTok and others"
ওই ভিখারি যেখানে ছিলো সেখানে যাওয়ার ব্যাবস্থা করো,0,"Meme, TikTok and others"
বসের সাথে একমত,0,"Meme, TikTok and others"
এটাকে ঝাড়ু দিয়ে পেটানো উচিত,0,"Meme, TikTok and others"
দুই জনের মুখে জুতামার,0,"Meme, TikTok and others"
আমার কিছু শর্টফিল্ম ভিডিও আছে খুব সুপার হিট,0,"Meme, TikTok and others"
সামনে পেলে আলু ভর্তা বানিয়ে দিতাম,0,"Meme, TikTok and others"
আপনি আমার সোনার খবর সোনালেন সৌদি আর ইরান কি বলছ সেটা না বলে আমার সোনা কইলেন আপনি,0,"Meme, TikTok and others"
শাকিবের কথা ঠিক আছে একদম,0,"Meme, TikTok and others"
তোর মা#,0,"Meme, TikTok and others"
ওকে জেনত ফুরিয়ে মেরে ফেলাহোক,0,"Meme, TikTok and others"
পৃ‌থিবীর শেষ সময় চ‌লে এসে‌ছে,0,"Meme, TikTok and others"
ইনশাআল্লাহ শাকিব খান অপু অাপুর কাছে ফিরবে এই অামাদের দোয়া রইলো,0,"Meme, TikTok and others"
আপার সাইজটা শো করলে মেয়েরা উদ্বুদ্ধ হতো,0,"Meme, TikTok and others"
ভারতের জনগন মোদী সরকারকে ভালবাসে না মোদী সরকার যুদ্ধের জন্য পাগল,0,"Meme, TikTok and others"
বালের অপরাধ,0,"Meme, TikTok and others"
দুইজনকে অনেক ভালো মানাইছে,0,"Meme, TikTok and others"
মোদি উপর আল্লাহর গজব,0,"Meme, TikTok and others"
স্বাধীনতা চাই,0,"Meme, TikTok and others"
ওকে জেলে নিয়ে খাওয়াবার দরকার নেই শাস্তি হলো ওর ননুর গোরা দিয়ে কেটে দাও,0,"Meme, TikTok and others"
কাশ্মীরে,0,"Meme, TikTok and others"
মুদিকে হাটাও,0,"Meme, TikTok and others"
ভারতীয় রা জংগী কাশ্মীর রা নয়,0,"Meme, TikTok and others"
অতিন্দ্রদার ফ্যানদের একটা লাইক হয়ে যাক,0,"Meme, TikTok and others"
ওকে খুব মারা উচিত তবু কেও মারলোনা কারণ সবাই ভদ্র ছিল কিন্তু এসব জানোয়ার কেন পাড় পাবে,0,"Meme, TikTok and others"
একটা ভিকারি নিয়ে এতো মাতা মাতি কেন মিডিয়ার মাথা ঠিক আছে তো,0,"Meme, TikTok and others"
এই তুই নামাজ নিয়ে গালি দিলি কেনো,0,"Meme, TikTok and others"
নাউজুবিল্লাহি মিন জালেক ইয়া আল্লাহ আমরা কোন জগতে বাস করি তুমি জানো,0,"Meme, TikTok and others"
তুমি আর খবর করো না তোআগে কথা বলা শেখ ভালো করেতারপর খবর করো,0,"Meme, TikTok and others"
বাবরি মসজিদ ফেরৎ দিতে হবে আমরা বাবরি মসজিদ ভাঙতে দেবনা আমাদেরকে আন্দোলন গড়ে তুলতে হবে আমীন,0,"Meme, TikTok and others"
কথা যাই বলুক না কেন সেলিব্রেটিদের কিছু ভুল আছে তারা রানু কে পেয়ে না জানি কি পাইছে আমাদের বাংলা কথায় যেটা বলে পাইয়া না পাইয়া পাইছে একবারে মাথায় তুলে ফেলছে একদিনে এখন মাথায় উঠে ডুগডুগি বাজাচ্ছে রানা মন্ডল,0,"Meme, TikTok and others"
শাকিব কে বহিস্কার করা উচিৎ,0,"Meme, TikTok and others"
সবাই চেনেটার জন্য রিপোট করিন এগুলা সব মিছা বলছে,0,"Meme, TikTok and others"
অকে চরম শাস্তি হক,0,"Meme, TikTok and others"
আমি চাই মসজিদ নির্মাণ করা হোক,0,"Meme, TikTok and others"
মোদী আর অমিতশা ভারতকে দংশ করছে আমি বাংলাদেশী আমি আমার দেশের সাথে,0,"Meme, TikTok and others"
আমি আছি তোমাদের জন্য ফ্রি,0,"Meme, TikTok and others"
না ঠিক আছে মেয়েটির সাথে নয়ন আগে জোর পুর্বক সম্পর্ক করে কারন নয়ন একজন সনএাসি ও আওয়ামীলিগ কেড়ার বুজেন তো বেপারটা আমরা ও প্রথমে এমনটা ভেবেছি পরে অনেক কিছু জানতে পারিআসলে পরিবারের বয় সবার আছে এখনকার আওয়ামীলিগের কর্মী বল্লে পুলিশ ও বয় পায় থাকতো সাধারণ মানুষ নয়ন খারাপ ছেলে বলেয়তো মিন্নি তার সাথে সম্পর্ক চিন্ন করে পরে রিফাত শরিফ কে বিয়ে করেআপনারা বলুন আপনারা বলুন আমি একটা খারাপ ছেলে কিন্তু আমার অনেক দাপট আছে আবার আমি একজন ছাএলিগ কর্মী এই জন্য কি একটা ভালো শিক্ষিত মেয়ে আমার জন্য তার জীবন নষ্ট করবে তাই তিনি নয়নের অন্দকার জীবন থেকে সরে গিয়ে নতুন করে বাচতে চেয়েছেন এটা তার অপরাধ নয় কিছু তে হতে পারেনা আর রিফাত শরিফ নিজেয়মিন্নি কে সবজেনে শুনে পচন্দ করে বিয়ে করেন মিন্নির বিয়ে হয়ে গেছে জান্তে পেরে নয়ন রেগে যায় নয়ন ভাবছেতার বয়ে মিন্নি কে বিয়ে করবে না রিফাত মিন্নি কে বিয়ে করে সাহসীকতার পরিচয়দে অবশেষে নয়ন বাহিনীর হাতে খুন হন আমাদের কাছে রিফাত একজন বিরউওমএকজন রিফাত নিজেরইস্তির ইজ্জত রক্খায়জিবন দিয়ে হাজার হাজার নারীর ইজ্জতকে সেফ করে গেছেন এটা হয়তো রিফাত নেয় কিন্তু তার ভুমিকা মানুষের অন্তরে রয়েযাবে চিরকাল আমরা মনে করি মিন্নি কে নিয়ে বাজে মন্তবো করাটাহবে খুনিদের সহায় করাতাছাড়া আরকিছুনয়,0,"Meme, TikTok and others"
শাকিব ওপু ছবি করুক সেই হবে,0,"Meme, TikTok and others"
কলকাতার প্রসাশন তো এর বিচার করবেইকিন্তু কলকাতার মানুষের কাছে একটাই আবদার যে যেখানে কুলাংগারকে পাবেন নিজের মত করে আবার বিচার করবেনতখনই প্রত্যেকটা ঘরের বৃদ্ধ বাবা মা এরকম কুলাংগার জালিম থেকে মুক্তি পাবে,0,"Meme, TikTok and others"
সুলে চরাও সালারে সালা তো মানুষ না কুত্তা,0,"Meme, TikTok and others"
হারকিউলিস বাংলা ভাষায় ♥♥ হাতেম বাংলা ভাষায় ♥♥ আলিফ লায়লা বাংলায় সিজন এবং ♥♥ বিয়ের গান ♥♥ কার্টুন বাংলায় ♥♥ সিনবাদ ও ইউসুফ জুলেখা বাংলায় ♥♥,0,"Meme, TikTok and others"
পানি না কিসের গরম তুমি ভুরা জানো না,0,"Meme, TikTok and others"
কুত্তার পেটে কি আর ঘি হজম হয়,0,"Meme, TikTok and others"
আমরা সবাই চাই আপনারা মিলে মিশে থাকেনআশা করি কম হলেও দশ কোটি মানুষ আপনাদের ভালো ভাসেন দয়া করে তাদের মন নষ্ট করবেনা সাকিব ভাইয়া,0,"Meme, TikTok and others"
আমি কি আপনাকে কল করবো না আপনি আমাকে কল করবেন,0,"Meme, TikTok and others"
সেখানে যে রামের জন্ম হয়নি সেটা কি তুমি প্রমাণ দিতে পারবে,0,"Meme, TikTok and others"
আর বালো লাগেনা ভাই জেখানে জাছি শেখানে তারা মা মেয় আর কত দেখাভে তাদের,0,"Meme, TikTok and others"
শাকিব পূণিমা চাই,0,"Meme, TikTok and others"
সেফাতুল্লাহ ওরফে শিবুদা ও বড় নাস্তিক,0,"Meme, TikTok and others"
রানুদির মুখ থেকে তো কখনই মেয়ের বদনাম শুনিনিতাহলে আপনারা কেনো ওনার মেয়েকে নিয়ে বাজে কথা বলছেন,0,"Meme, TikTok and others"
মোঃ আনোয়ার হোসেন,0,"Meme, TikTok and others"
গনিস্তকিবুজিয়েবলুন,0,"Meme, TikTok and others"
একটাও না কারন অপু নাই,0,"Meme, TikTok and others"
তোর হোলে চুল উটি ছে তোর কেউ পুঙা মেরেছে নাকি,0,"Meme, TikTok and others"
বোকা চোদা,0,"Meme, TikTok and others"
সাকিবের পাশে অপু কে সবসময় দেখতে চাই,0,"Meme, TikTok and others"
অপু একটা খারাপ মেয়ে,0,"Meme, TikTok and others"
কেউ পড়ালেখা না জানলে মূর্খ হয় না অক্ষরজ্ঞানহীন হয়আপনার অত ঠুকু বুঝার বয়স হয় নাই,0,"Meme, TikTok and others"
এমন দৃশ্য শয্য করা যায় না অাল্লাহ তু‌মি মানুষের মানবতা এতটা নি‌চে নাম‌তে দিও না শয়তান‌কে এতটা ছে‌ড়ে দিও না শয্য করা যায় না,0,"Meme, TikTok and others"
কাসমির মুক্তি পাক,0,"Meme, TikTok and others"
ইন্ডিয়া দেশ টা এই রখমকারো মনে রহমত নাই,0,"Meme, TikTok and others"
নরো পশু,0,"Meme, TikTok and others"
মিডিয়া কি পাগল না কি,0,"Meme, TikTok and others"
মেয়ের চ কান্ত এটা,0,"Meme, TikTok and others"
আপনাকে ধন্যবাদ এবং সাকিব এবং অপুর সংসার ভালো থাকক আমিন,0,"Meme, TikTok and others"
নয়ন কে বাচানুর চেসটা,0,"Meme, TikTok and others"
বিএনপি রাজাকারদের নিয়ে গঠিত বাংলাদেশ বিরোধী একটি অপশওি,0,"Meme, TikTok and others"
সাকিবকে বহিষ্কার করা হোক,0,"Meme, TikTok and others"
ছেলেটিকে পুলিশ গ্রেপ্তার করে একে ধুম মারধর করেন,0,"Meme, TikTok and others"
মুদি তোর দিন শেষ সব,0,"Meme, TikTok and others"
আমি চাই শাকিব খান সাথে অপু আমাকে,0,"Meme, TikTok and others"
ধরে পিটাও জানোয়ার টাকে শাস্তি চাই এই রকম কাজ কেউ জেনো করতে না পারে,0,"Meme, TikTok and others"
এমন পুলিশ ভাইদের কে মন থেকে স্যালুট স্যালুট স্যালুট,0,"Meme, TikTok and others"
বেইমান তাহলে দেখানোর দরকার ছিল,0,"Meme, TikTok and others"
প্রথমে ময়রিকে দেখলামতার পর সবার কমেন্ট গুলা পরি,0,"Meme, TikTok and others"
এই চেলেকে কি বলবো আমি,0,"Meme, TikTok and others"
প্রতিটা চর যেন আমার কলিজাতে লাগলো,0,"Meme, TikTok and others"
আমি কাশ্মীরে পক্ষে,0,"Meme, TikTok and others"
নবী নিয়া তুই গালাগালি দিস শালা অশিক্ষিত,0,"Meme, TikTok and others"
খবর বাদদিয়ে বাল ছিড়ে আটি বাদ,0,"Meme, TikTok and others"
কপাল ভালো বাংলাদেশে এমন হলে খুব কঠিন শাস্তি দিতো জনগন ওর ফাসি চাই কিভাবে বাবার গায়ে হাত দেয়,0,"Meme, TikTok and others"
তার মনুষ্যত্ব প্রশ্নবিদ্ধ,0,"Meme, TikTok and others"
বুবলি পিট আচে,0,"Meme, TikTok and others"
তুমিয হিন্দু মেয়েদের ছবি দিলা কেনকয়ডা বোকরা আলির ছবি দিতা,0,"Meme, TikTok and others"
যাদের পুরুষ কল গার্ল প্রয়োজন তারা এই নাম্বারে ফোন দিবেন আমাদের লোক বাসায় চলে যাবে,0,"Meme, TikTok and others"
শরেরবাছাকেকেটেফেলেদাঔ,0,"Meme, TikTok and others"
ওর মুভি কেও দেখা নাকি ফালতু নায়ক,0,"Meme, TikTok and others"
ওকে একলা নিচ্ছেন কেনো ওর বউ কে ও নিয়ে যান বউ হলো মেন বউ বিচার দিছে,0,"Meme, TikTok and others"
আমি কাশ্মীর চাই,0,"Meme, TikTok and others"
কষ্টে বুকটা ফেটে গেলো আমার,0,"Meme, TikTok and others"
ওর ঠিকানাটা বলেন ওর মাইরা ফাটাইয়া লামু,0,"Meme, TikTok and others"
খবর তৈরি করতে পারেন কিন্তু আটকাতে পারেননি,0,"Meme, TikTok and others"
রানুদির আজও সতভাগ মানসিক শক্তি ঠিক নয় কথা কিছু টা এলোমেলো,0,"Meme, TikTok and others"
আল্লাহ তুমি এই কুলাঙ্গার সন্তানকে দুনিয়ায় বিচার কর,0,"Meme, TikTok and others"
এই নম্বারে ফোন দিয়া বলো কখন আসবো,0,"Meme, TikTok and others"
পরিচালক সমিতিরা তাদের কথা ভাবচে দেশের কথা নয় আজ আমাদের চিত্রজগত যে খানে এসে দারিয়েছেএবং বাংলাদেশকে এগিয়ে নিয়ে জাচ্চে তার অবদান হল সাকিব খানতাহলে পরিচালক সমিতিরা কেন বুঝতে চাইচেনা এই চিএ জগতে সাকিবই হল একটা বট গাছচলো আমরা সবাই এক হয়ে পতিবাদ করি,0,"Meme, TikTok and others"
কুব ভাল,0,"Meme, TikTok and others"
যে হাত দিয়ে তার বাবাকে মেরেছে তার হাত দুটি কেটে দেওয়া হক আর যাতে করে কেউ এমন করতে না পারে,0,"Meme, TikTok and others"
ভারত হিন্দু রাষ্ট্র হবে তোর্ কী ভাগ,0,"Meme, TikTok and others"
আমি ভলব কোরান এ কি আছে সেই অনুযায়ী ব্যবস্থা নিবেন,0,"Meme, TikTok and others"
জয় বাংলা জয় হিন্দ,0,"Meme, TikTok and others"
কয়লা ধুইলে ময়লা যায় না,0,"Meme, TikTok and others"
কাসমির জিনধাবাত,0,"Meme, TikTok and others"
জয় একটু বেশি কতা বলে,0,"Meme, TikTok and others"
অসাধারণ কথা বলেছেন,0,"Meme, TikTok and others"
এ সব ছবি দেখিয়ে মানুষের ঈমার কেড়ে নিচ্ছেনআল্লাহর কাছে কি জবাব দিবেন এমন ধরনের ভিডিও না বানানোর অনুরোধ করলাম,0,"Meme, TikTok and others"
তার জন্যও কঠিন কিচু অপেক্ষা করতেছে,0,"Meme, TikTok and others"
কোন জিজ্ঞাসা বাদ ছাড়াই পশুটাকে ফাঁসি দেওয়া হোক,0,"Meme, TikTok and others"
ভয়াবহ খবর পাকিস্তান পুনরায় বাংলাদেশ দখল করে নিল এবং এই কাজে রোহিঙ্গারা পাকিস্তানের সমর্থন করলেন,0,"Meme, TikTok and others"
শ্রী জিত মুখার্জি পরিচালক হিন্দু ব্রাহ্মণ আর গরুর মাংস খেয়েছেগো মাঙস খাওয়া না প্রত্যেকের নিজস্ব রুচির পরিচয়কেউ কেউ ভাবেন যে গরুর মাংস মুসলমানদের খাদ্যসে মুর্খের স্বর্গে বাস করছে পৃথিবীর ইতিহাসে সব প্রধান ধর্মে গো মাঙস খাওয়া প্রচলন ছিল আছে হিন্দু মুসলিম খৃস্টান ধর্মের পন্ডিতের জিগ্গেস করলেই বুঝতে পারবেন কাউকে কষ্ট দিতে লিখিনি সত্যটি বলার চেষ্টা করেছি মাত্র,0,"Meme, TikTok and others"
শাকিব অপু মিলিয়ে চাই,0,"Meme, TikTok and others"
ড্রেস দেখলে প্রোধানমণ্ত্রী বুঝতে পারে এই মণ্ত্রী পাগল হয়েছে নাকি এসব ভূয়া কথা আর যদি সত্যি প্রোধানমণ্ত্রী এই ধরনের কথা বলে থাকে তাহলে এটা পুরাপুরি মুসলিম বিরধীতা মণ্ত্রী #,0,"Meme, TikTok and others"
আল্লাহ তুমি এগুলো দেখোনা ওর বিচার করোনা কেনো এই জমিনেই বিচার করো,0,"Meme, TikTok and others"
তাহুলে মুসলমান এভাবে মরবে আর আরেক মুসলমান ভাই চেয়ে থাকবে,0,"Meme, TikTok and others"
বাপের বেটা আব্রাম খান জয়,0,"Meme, TikTok and others"
আমি আশব,0,"Meme, TikTok and others"
মরন কর,0,"Meme, TikTok and others"
অরে তোমার দুধ যতটুক ওজন আমার সারা শরীলের ওজন ততটুক,0,"Meme, TikTok and others"
আমি তো প্রথম দেখে মনে করছি হিজরা,0,"Meme, TikTok and others"
কুতারবাচা,0,"Meme, TikTok and others"
এত খারাব চুদা ল,0,"Meme, TikTok and others"
ড়িচি সালা সরকারি কাচনাকরে মেয়েকে দেকচে সালারে কটিন বিচার চাই চাকরি না,0,"Meme, TikTok and others"
মোদির বিপখে,0,"Meme, TikTok and others"
জামালপুর ই সেরা,0,"Meme, TikTok and others"
এ নায়ক দর‍কার‍ নেই আমি হব নায়ক,0,"Meme, TikTok and others"
শাকিব খান আপনি আর কয়টা বিয়ে করবেন আপনার থেকে অপু বিশ্বাস অনেক ভালো আছে আশা করি ভালোই থাকবেন এই জন্য অপু বিশ্বাস কে এত ভালো লাগে,0,"Meme, TikTok and others"
উগানডার আর উলু লুলুর ফুরিন কিলা তাকইন অতা নিয়া ভিডিও বানাইয়া দিয়,0,"Meme, TikTok and others"
কত্তার বাচ্চা,0,"Meme, TikTok and others"
আমার কাছে অনেক ভালো লাগলো মমতাজ আফু থাকার জন্য,0,"Meme, TikTok and others"
আমরা ববলিকেস বাদ দিলে অনেক খুশি হয়েছি,0,"Meme, TikTok and others"
তাকে উচিত শাস্তি দেয়া হোক,0,"Meme, TikTok and others"
আমরা ভারতীয় মুসলিমরা বাংলাদেশের বেইমান সরকার এর পক্ষে নয়বাংলাদেশ ভারতের দালাল,0,"Meme, TikTok and others"
হিন্দু হিন্দু তুলসী পাতা জয় আর পূর্ণিমা আতা আমার পোতা,0,"Meme, TikTok and others"
রাইট শাকিবের দিতিও পাট বাপি,0,"Meme, TikTok and others"
নামবারটা দেও কথা বলি,0,"Meme, TikTok and others"
ওরে জুতা মার,0,"Meme, TikTok and others"
সবার কি সবকিছু সহ্য হয় রানু ও সেই অবস্থা,0,"Meme, TikTok and others"
বুখারীর প্রতি মল মিশ্রিত ছেড়া ও বুড়া জুতা নিক্ষেপ করলাম সে ছদ্মবেশি,0,"Meme, TikTok and others"
সাকিব থেকে জয় লেখা পড়ায় এগিয়ে যাক এটা আমরা চাই,0,"Meme, TikTok and others"
শাকিব এর পরিচয় চিএ জগত থেকেএটা নাথাকলে শাকিব বেকারতাই ওকে এবং আপু ইসলাম খানকে সরত্ সাপেক্ষানুযায়ী মিশিয়ে দিয়া ওদের ছেলেটিরলাইফ ঠিক করে দিন ওরা মিল হলে ভাই এবং বোনের ছেলে হিসাবে আগামী বাডডে আমি বিদেশে বসে করবোকারন আমি মোনে করবো জয় আমার বড়ভাইয়ের ছেলে,0,"Meme, TikTok and others"
পিছনের দুইজন মনে হয় বাংলা বুঝে না,0,"Meme, TikTok and others"
কোথা থেকে যে এই সব খবর পায় বাঙালি আমি নিজেও আর্জেন্টিনা সমর্থন করি,0,"Meme, TikTok and others"
চারাল সব মাইরালা সাথেমোদিরেও মার,0,"Meme, TikTok and others"
নেএকোণা মেয়েরা,0,"Meme, TikTok and others"
ইরান রাইট,0,"Meme, TikTok and others"
কুতত,0,"Meme, TikTok and others"
মাই গড দুধু নাকি,0,"Meme, TikTok and others"
সত্যা কী শাকিব আর অপু সম্পকো মিলে গেছে,0,"Meme, TikTok and others"
কমেন্ট পরে মনে হলো দুধ নিয়ে একটা রচনা লেখা দরকার কি বলেন সবাই,0,"Meme, TikTok and others"
ভিকারি কে খমা কেউ কোরবেনা,0,"Meme, TikTok and others"
জয় শীরাম,0,"Meme, TikTok and others"
বাটপারি করসেন কেনো বিগুতে কুন মেয়ে কি বিবাহ করে দেকাতে পারবেন দেন তো দেকি আপনার সামি কেমন এতো জাসাই বাচাই করসেন চেলেদের ভাডী গেইঠে ডুকতেও দীবেনা,0,"Meme, TikTok and others"
আল্লাহ পাক জাকির নায়েকের হেদায়েত দান করুন আমিন,0,"Meme, TikTok and others"
উচিত শিক্ষা হইছে,0,"Meme, TikTok and others"
হে প্রভু তুমি আমাদের সবাইকে হেদায়েত দান কর আমিন,0,"Meme, TikTok and others"
ওর মুখ টয়লেট আকৃতির ওখানে পায়খানা করে আরাম পাওয়া যাবে,0,"Meme, TikTok and others"
হিমেশ ও রানু দির গান অনেক সুন্দর,0,"Meme, TikTok and others"
কল দিও সোনা আমার,0,"Meme, TikTok and others"
কাশ্মির এখন নতুন নরক তৈরী করছে,0,"Meme, TikTok and others"
আর কি করলে হবে অপরেশান না করে,0,"Meme, TikTok and others"
এমপির ফোলারে দরা হোক,0,"Meme, TikTok and others"
বালো লগলো,0,"Meme, TikTok and others"
দেখতে খারাপ লাগছে,0,"Meme, TikTok and others"
আমিরাশীরনয়তবেআপনারকথা,0,"Meme, TikTok and others"
শাকিব৷ হলো৷ একটা৷ লুইচ্চা,0,"Meme, TikTok and others"
ভিডিও পাঠান,0,"Meme, TikTok and others"
এই রায় মানী না আমার আল্লাহ বিচার করবে ইনশাআললাহ,0,"Meme, TikTok and others"
ইসসস কলিজাটা ফেটে যাচ্ছে একজন বৃদ্ধ বাবাকে এভাবে মারে,0,"Meme, TikTok and others"
আমি জোদি ওর কাজে থাকতাম তা হলে সালারে মারতে মারতে পাখানা করাই তাম আর আমি কি করতাম আমি কিচ্চু জানি না বাই বিসাষ করেন,0,"Meme, TikTok and others"
নাজুবিলল্লাহ এতো কারাপ কথায় বলে কি বাবে চি চি চিই,0,"Meme, TikTok and others"
পিকসতিন,0,"Meme, TikTok and others"
প্ররোচিত রায় বিশ্বে জাতী ও সুঃকোটের মর্যাদা ক্ষুণ্ণহবেবাস্তবায়নের চেষ্টাকরা কতটুকু ফলপরশু হবে কঠিন বিষয় সরকারের সান্তিরজন্ন আপিলের মধ্যে কালক্ষেপনের মধ্যে হিন্দু মুসলিমদের উত্তেজনা পরসমিতকরে সঠিকবিচার করুন ইসলামে মজিদের স্থানে মজিদ থাকে এইকারনে ছাড়দেয়া জায়না,0,"Meme, TikTok and others"
জিন্দাবাদ জিন্দাবাদ,0,"Meme, TikTok and others"
উচিত শিক্ষা হইছে এমন সব কুলাঙ্গাররা এমন কাজ করার আগে হাজার বার চিন্তা করবে,0,"Meme, TikTok and others"
ঠিক বলছেন ভাই এরকম বিয়াদব নায়ক চাই না,0,"Meme, TikTok and others"
ছেলে আর ছেলের বউকে পিটিয়ে জুতার মালা গলাই দিয়ে থানাই পাঠিয়ে দেন এলাকা বাসির কাছে বাংলার মানুষের বিনিতো অনুরদ,0,"Meme, TikTok and others"
ওর বাবাকেও যেভাবে মারতেছেবুঝা যাইতেছে এভাবে মারাটা ছেলে ও তার বউয়ের নিত্য ব্যাপারমাননীয় সরকারের কাছে অনুরোধ এ ধরনের ছেলেদের দৃষ্টান্তমূলক মূলক শাস্তির আইন চালু করতে,0,"Meme, TikTok and others"
আমরা সবাই আছি আপনার দে সাথেই আছি,0,"Meme, TikTok and others"
অতিন্দ্র দা তবে রাণু দির মেয়েকে তাড়াও,0,"Meme, TikTok and others"
কাসমির জিদবেইইনশাআল্লাহ,0,"Meme, TikTok and others"
এই বাস্টার ডের বহিস কার করা টা অনেক দেরি হয়ে গেল,0,"Meme, TikTok and others"
মুহাম্মদ কে নিয়ে কথা বললি কার সাহসে দেখ তাসি,0,"Meme, TikTok and others"
অপু কে চাই,0,"Meme, TikTok and others"
আমার অনেক কষ্ট লাগছে এরকম ছেলেকে ফাঁসি দেওয়া উচিত উনার আমি ফাঁসি চাই,0,"Meme, TikTok and others"
তাকে আল্লাহ কখনো মাফ করবেন না,0,"Meme, TikTok and others"
খুব খারাপ লোকবৃদ্ধ পিতাকে এভাবে মারছেনিশ্চয়ই এর ফল পাবে,0,"Meme, TikTok and others"
এই জগত টাই খারাপ যেখানে দেহের সাইজ ভালো কিনা টেষ্ট করতে হয় আগে,0,"Meme, TikTok and others"
ওর মতো ছেলে কে আল্লাহ গজব পালাক,0,"Meme, TikTok and others"
ওরে পাইলে জবাই করতাম খোদার কছোম,0,"Meme, TikTok and others"
সাকিব ভাইয়া সাথে আমি একমত,0,"Meme, TikTok and others"
রানুদি ও ওর মেয়ে দুজনেই ছোটোলোকআর কোনো কথা হবেনা,0,"Meme, TikTok and others"
আল্লাহ সবাইকে হেদায়েদ দাও,0,"Meme, TikTok and others"
গুম খুন রেপ কিছু বলবেন না মানে নিজ ভূমি নয,0,"Meme, TikTok and others"
কাশ্মীরের,0,"Meme, TikTok and others"
মা বাবার গায়ে হাত তুলেছে আল্লাহর আরস কেপে উঠবে অকে মেরে চামরা ওঠিয়ে ফেলুন,0,"Meme, TikTok and others"
ডাঃ তসলিমা অন্তত কিছু রোগী সেবা করো দেশে এসে,0,"Meme, TikTok and others"
এখানে দেখলাম অনেকেই কারাপ কমেণ্ঠ করেছে সেইটা ভাল করেনিকারন সাকা রাজাকার কখনো ছিল না এবং তার মত অন্য কোন নেতার জম্ম হবে না আমি বঙ্গবন্ধু ও আওয়ামীলীগকে ভালবাসি তাই বলে কি সাকা কে রাজাকার বলতে হবে না খকনো না,0,"Meme, TikTok and others"
রোজ কম হলে,0,"Meme, TikTok and others"
আখেরাতে তর কি অবস্থা হবে আল্লাহ ভালো জানেন,0,"Meme, TikTok and others"
তার ঠিকানা পাইলে তারে ঠিক গারায় ফালাইতাম,0,"Meme, TikTok and others"
সে যদি নাই কেনে বিয়া করব না তাহলে নায়িকার সাথে বসর সম্পর্ক করল কিভাবে এটা আমার কথা নয় এটা শাকিব পরিদর্শকের কথা,0,"Meme, TikTok and others"
ঐ ছেলের বিচার চাই বিচার চাই বিচার চাই,0,"Meme, TikTok and others"
চট্টগ্রামের বাঘ বার নির্বাচিত সংসদ সদস্য অফুরন্ত দোঅা এবং ভালবাসা রইলো সাকা স্যারের জন্য আল্লাহ তাকে জান্নাতের উচু মোকাম দান করুনআমিন,0,"Meme, TikTok and others"
প্রকৃতি কখনও কারও ভার নেয় নাওমন ছেলে যেন কারো গর্ভে না আসে,0,"Meme, TikTok and others"
নাওজুবিল্লা,0,"Meme, TikTok and others"
মালাউন তুরা দংস হবে,0,"Meme, TikTok and others"
ভালোই লাগে আবার খারাপও লাগে,0,"Meme, TikTok and others"
সবই আল্লাহর লিলা খেলা আমিন,0,"Meme, TikTok and others"
পুরো অনুষ্ঠান পূর্ণিমার আলোয় আলোকিত ছিল,0,"Meme, TikTok and others"
বাংলাদেশের ইউটুবার সস্তা নেশা করে ভিডিও বানাই এটা পাক্কা পারলে থেকে তথ্য নিয়ে ভিডিও বানাও ভিউ পাওয়ার জন্য উল্টো পাল্টা ভিডিও না করাই ভালো,0,"Meme, TikTok and others"
না আমি চাইনা আমি চাই অপু শাকিবের চেয়ে অনেক ভালো থাকুক,0,"Meme, TikTok and others"
কাশ্মীর ভারতেরই অংশ,0,"Meme, TikTok and others"
রানু দির মেয়েকে মেন্টাল হসপিটাল এ পাঠানো হোক,0,"Meme, TikTok and others"
মিন্নিকে ফাসি দেওয়া হোক ও একটা নষ্টা মেয়ে,0,"Meme, TikTok and others"
আল্লাহ এরকম ছেলেমেয়ে কারো ভাগ্য দিও না,0,"Meme, TikTok and others"
ফাসি দিয়ে দেয়া উচিত জনসম্মুখ্যে,0,"Meme, TikTok and others"
আমি সাকিভ কানের সাতে এক মত,0,"Meme, TikTok and others"
রানুদি জে হাতটা জোড় কোরে আছে ভালো কোরে সবাই দেখুন ওটা রানুদির হাত না নকল গুজব ভিডিও,0,"Meme, TikTok and others"
সত্যি বলতে এই ইউটিউব চ্যানেল টা একেবারে ফালতু সব সময় নায়ক নায়িকাদের বডি ফিগার এবং তাদের চরিত্র নিয়ে কথা বলে তাদের সম্বন্ধে কিছু ভালো কিছু উপহার দিতে পারেন না আজাইরা খালি খবর দেন,0,"Meme, TikTok and others"
তার বউ,0,"Meme, TikTok and others"
কু পুত্র চি চি,0,"Meme, TikTok and others"
এটা ময়ূরী না,0,"Meme, TikTok and others"
চোরের টা কে অর বারির ঠিকানা না দেন,0,"Meme, TikTok and others"
গরিব দিকে,0,"Meme, TikTok and others"
কাশমিজয়ইনশাআল্লাহইমরান খানকেকেনজেলেদিবেইমরান খানভালো,0,"Meme, TikTok and others"
সেলিম খানের ভাষায় বলছি পুরাণ ভুলে নতুন কিছু মনে পড়বে না তো,0,"Meme, TikTok and others"
আপু প্লিজ প্লিজ আমার চ্যানেলটি সাবস্ক্রাইব করুন,0,"Meme, TikTok and others"
পাকিস্থানের পক্ষে,0,"Meme, TikTok and others"
পালটু,0,"Meme, TikTok and others"
নাইকা হিসেবে গুড কে আপন কে পর সিরিয়াল টা বাজে এক এক করে পরিবারের সকলের সাথে দুশমনি চলতেছে,0,"Meme, TikTok and others"
এরা জীবনেও শোধরাবে না,0,"Meme, TikTok and others"
এক সময়ের ক্রাশ ময়ূরী,0,"Meme, TikTok and others"
অনন্ত জলিল দাবি করলো আর হলো🤣,0,"Meme, TikTok and others"
এর কঠিন শাস্তি হওয়া উচিৎ এর বউ ও এই রকম তানা হলে কেনো তার স্বামীকে আটকালোনা,0,"Meme, TikTok and others"
কাশ্মির তারা আমাদের ভাই বোন মুসলিম অামরা শুতায় গাথা ভারতিয়রা নিমক হারাম মিরজাফর,0,"Meme, TikTok and others"
হুমম এক মত,0,"Meme, TikTok and others"
অতীন্দ্র দা তুমি কেন এখনো ও বেইমান রানুর পাশে আছো সরে যাও রানু ভুজবে তখন,0,"Meme, TikTok and others"
ওর,0,"Meme, TikTok and others"
ভিডিও টা দেখে আমার ইমারজেন্সি তে কাল হাসপাতালে ভর্তি হতে হয়েছিল খুব খুব কস্ট লেগেছেএমনদিন আল্লাহ আমার শত্রু কেও না দিক৷ বাবা মা আছে যাদের আল্লাহ এর কাছে হাজার শুক্কুরএতিম রাই বুঝে বাবামা কি আল্লাহ যদি আমাকে তৌফিক দিত এ বৃদ্ধ লোক আর তার বউকে আমি এডপ্ট করে নিজে খাইয়ে পরিয়ে পালতাম আমার দাদা দাদি নানা নানি নেইআমার আম্মু আব্বু অনেক কস্ট পায়,0,"Meme, TikTok and others"
তার ফাঁসি কবে হবে,0,"Meme, TikTok and others"
সাকিব এ কথা কাজে করে দেখাও,0,"Meme, TikTok and others"
আপু ককচ্ছবাজারের মেয়েরা কেমন বলেন নাই,0,"Meme, TikTok and others"
তৃণমূল মানে চোরেদের আতুর ঘর,0,"Meme, TikTok and others"
ভারতের সব কথা মিথ্যা,0,"Meme, TikTok and others"
খুব সরল একটা মানুষ,0,"Meme, TikTok and others"
পাকিস্তান ☝️☝️☝️,0,"Meme, TikTok and others"
ছাই‌ আমি মুননিকে নাইকা হিচাপে ব্যৱহাৰ,0,"Meme, TikTok and others"
আমরা চাই শাকিব অপু জটি হোক বুবলী বাদ একটা খারাপ মেয়ে,0,"Meme, TikTok and others"
নতুন নতুন গানের আপডেট পেতে চ্যানেলটি সাবস্ক্রাইব করুন,0,"Meme, TikTok and others"
মিথিলার ভিডিও লিংটা কারোর কাছে থাকলে দয়া করে দিবেন,0,"Meme, TikTok and others"
আস্তাগফিরুল্লাহ বেটা ফাজিল তুমি মাতালে বিভোর আছতুমি বাংলায় কথা বলছঅথছ তুমি নিজেকে বিদেশি দাবি করছ বেয়াদবযত গালি দিয়েছ তুমার উপড়ে আগে পড়েছেকারন তুমি বাংগালীর পয়দা না হলেবাংলায় কথা বলতে পারতেনাবেয়াদব,0,"Meme, TikTok and others"
সানাই কই,0,"Meme, TikTok and others"
আপু আপনি একদম ঠিক কথা বলেছেন,0,"Meme, TikTok and others"
ওরে কি বলবো ওর এলাকার মানুষ ওরে মেরে ফেলেনা কেনো,0,"Meme, TikTok and others"
আল্লাহ আপনি এর বিচার করুন,0,"Meme, TikTok and others"
ময়ূরকে অনেক সুন্দর লাগছে,0,"Meme, TikTok and others"
সাবই মিলে তার মুখে দিয়ে বগা ডুকাই আসো,0,"Meme, TikTok and others"
এটা সম্ভবত ভারতের ঘটনা,0,"Meme, TikTok and others"
খেলার খবর নাই,0,"Meme, TikTok and others"
ৃকাশ্মিরি জনগন যা চায় বিশ্বের নিরিহ মানুষ তাই চায় জুলুম নির্জাতন বন্দকরা দরকার,0,"Meme, TikTok and others"
মোটা হলে ও ময়ুরীকে ফেইসটা ভাল লাগছে ভাল আর্টিস্ট ছিল,0,"Meme, TikTok and others"
ভুং ভাং না দিয়ে ভালো,0,"Meme, TikTok and others"
ছি এতো নিচে মানুষ নামতে পারে,0,"Meme, TikTok and others"
আপু ভালো,0,"Meme, TikTok and others"
এইটাতো ঠিক একাকত বছর থাকবে,0,"Meme, TikTok and others"
মেএটির গায় একটাও কাটা ছিরার দাগ নেয় আর ঠান্ড মাথার পেলেন করে এসপ করা হোলো আমার মনে হয়া ও দায় আছে আমরা ফাসি চায় জারা জারা ছিলো সবার আমি বাংলাদেসের নাগুরি বলতে গৃনা করে এটা আমার দেস বলতে গৃনা হয় হায়রে দেসের বিতু মানুর বাবছি আর তেসে জাবোনা,0,"Meme, TikTok and others"
তোদের মতো বাজে মেদের ফাদে জেসব ছেলেরা পাদেয় তারাও ছেলে নামে বনচিতো নাম্বার না চেয়ে একটা করে জুতা মারতে পারেনা,0,"Meme, TikTok and others"
তাই না কি @@@@@@@@@@@@@@@@@@@@@@@@@@@@ দারুন,0,"Meme, TikTok and others"
এই রকম ছেলে,0,"Meme, TikTok and others"
এই ভিডিও প্রায় বছর আগের,0,"Meme, TikTok and others"
এবং সাকিব আখেরাতে ও ভালো পাবে,0,"Meme, TikTok and others"
অনেক শিল্পিকে দেখেছি এই ধরনের বেবহার কনো শিল্পি করেনি,0,"Meme, TikTok and others"
প্রিয় ভালবাসার উপস্থপিকা আপনার কন্থ সর খুব সুন্দর প্রতিদিন প্রতি সময় সুন্তে চাই তমায়,0,"Meme, TikTok and others"
আপু সাকিব খান দুই জন নের দুস আছে আনেকে বলবেন আমার পরিচয় নামবার,0,"Meme, TikTok and others"
বুবলি কে চিনি না,0,"Meme, TikTok and others"
আল্লার গজব আশতেচে অপেক্ষা কর মাগি,0,"Meme, TikTok and others"
পাকিস্তান এর পক্ষে,0,"Meme, TikTok and others"
বিশ্বাস করিনা এটা জবার শরিল বলে,0,"Meme, TikTok and others"
আপনারা এক হন শাকিব খান অপু খান,0,"Meme, TikTok and others"
খুনের বদলে খুন,0,"Meme, TikTok and others"
আপনি কি পাগল,0,"Meme, TikTok and others"
আমি পাকিস্তানকে ছাপোট করি,0,"Meme, TikTok and others"
এই সিদ্ধান্ত এসব তাহসান মানুষের কাছে আইকনিক হিসেবে থাকবে আছে এবং থাকবে মিথিলা পতিতালয় থাকবে এটাই বাস্তবতা,0,"Meme, TikTok and others"
টাংগাইল সদর,0,"Meme, TikTok and others"
তোমার সাতে কথা বলতে চাই মিশ দিবো,0,"Meme, TikTok and others"
খারাপ বলে নাই,0,"Meme, TikTok and others"
মাপ কোরো,0,"Meme, TikTok and others"
গোসিপ🤣,0,"Meme, TikTok and others"
ওরে পাইলে যে কি করতাম আল্লাহ ভালো যানেতোরে গুলি করে মারতাম,0,"Meme, TikTok and others"
কাশ্মীরের পক্ষে নিব ভারতকে ছুড়ে ফেলে দিব,0,"Meme, TikTok and others"
হাঁ আমি ডক্টর জাকির নায়েকের ফেনতবে প্রথমেই জানতে চাই আপনাদের চেনেলটি কাদের দালাল হয়ে কাজ করার জন্য খুলেছেন ডক্টর জাকির নায়েক অবশ্যই চরম পন্থী মুসলমান ননতিনি সেই মুসলিম যা হবার জন্য আল্লাহ আল কোরআনে আমাদেরকে নির্দেশ দিয়েছেনএইতো সেই মুদী যাকে আমেরিকা মুসলিম নিধনের কারনে ভিসা দেয়নি আজ সেই মুদী মুসলিম মৌলবাদ নিয়ে কথা বলছে আর মুসলমানরা তা গিলে নিচ্ছে ডক্টর মহাথীরের বক্তব্যটি আমি শুনেছিএটা পলিটিকেল বক্তব্য বলে মনে হয়েছেইহা বুঝার জন্য ডক্টর মহাথীরের পরবর্তী বক্তব্য শুনা ও পুনঃ বিশ্লেষণ দরকার,0,"Meme, TikTok and others"
ধন্যবাদ দাদা আপনাদেরকে অনেক অনেক ধন্যবাদ,0,"Meme, TikTok and others"
সবার সেরা আমাদের শাবনূর,0,"Meme, TikTok and others"
শাকিব খানকে আইনের আউতায় আনা হোকআর যাতে কেউ এমন কাজ করতে না পারেএই শাকিবের মতো মানুষের জন্য আজ ছলএীতরের মানুষকে সম্মান দেয় নাদেখো কতো সুন্দর দিন কাটাচ্ছেন রিয়াজ ভাইআমিন খান ভাইইলাস কান্চন ভাই আলমগীর ভাই ফারুক ভাই মৌসুমি আপুশাবনূর আপু ও পূর্ণিমা আপু ওদেরকে সারা জীবন মানুষ সম্মন দিবে তুমার মতো শাকিব কে নয়,0,"Meme, TikTok and others"
আমরা আবারও মেসিকে চাই আমাদের মাধে,0,"Meme, TikTok and others"
কেমনআছেন,0,"Meme, TikTok and others"
ইস তরে যদি সামনে পাইতাম,0,"Meme, TikTok and others"
অপু একটা বেয়াদব,0,"Meme, TikTok and others"
এটা মিথ্যা কথা বুবলী সাকিব খানের সঙ্গে কাজ করতাছে,0,"Meme, TikTok and others"
পুতুল আমি নিবো এটা আমার নামবার আমি মালরাশিয়া আছি,0,"Meme, TikTok and others"
হায়রে এ কি দৃশ্য দেখছিএই ছেলেকে আল্লাহ তো জাহান্নাম এর আগুনে ফালাবে,0,"Meme, TikTok and others"
এতেরে কিছু বলেন হারামি,0,"Meme, TikTok and others"
কেমন অমানুষ যেমন ছেলে তেমন তার বউ,0,"Meme, TikTok and others"
ওর হাত দূটো কেটে ফেলা হোকওকে জদি আমি শামনে পেতাম৷,0,"Meme, TikTok and others"
এই লোককে আল্লাহ ছারবেনা,0,"Meme, TikTok and others"
ওরে জুতা মার সালা কুততা শয়তান,0,"Meme, TikTok and others"
নামাজ ছাড়া বিকল্প কিছু নেই আল্লাহ নিউজিল্যান্ডের সব শহীদদের বেহেশত নছিব করুন আমিন কে কে আমার সাথে একমত তারা কমেন্ট করেন এখানে,0,"Meme, TikTok and others"
পশুর থেকেও খারাপ,0,"Meme, TikTok and others"
ওরে আর কি গালি দিবো,0,"Meme, TikTok and others"
ইসলাম ধর্ম নিয়ে গালি দিবেনা পিল্জ,0,"Meme, TikTok and others"
আমি ত মেয়ে তবে মেয়েরাঅনেক খারাপ মেয়ে ত নারির জাত মায়ের জাত গালি না দিয়ে পারলাম না,0,"Meme, TikTok and others"
শাবাশ,0,"Meme, TikTok and others"
মমতা বেনাজি,0,"Meme, TikTok and others"
আমি ওদের সাথে যোগাযোগ করব কিভাবে,0,"Meme, TikTok and others"
মিন্নিকে নিয়ে জারা আজেবাজে কথা বলেন তারা কোন মানুষের কাতারেই পরে নামুখ খারাপ করলামনা আপনারা দয়া করে মিন্নিকে নিয়ে আর বাজে কথা বলে পাপের পাল্লা ভারি করবেন না অসহায় একটা মেয়েকে নিয়ে এতো মাতামাতি করার কিছু নাই সম্ভু ও ছেলে সুনামকে আর জারা জারা কোবাইছে এদের সবাইকে রিমান্ডে নেওয়া হোকদেশবাসী এটাই চায় বাংলাদেশে যত মাস্তানরা কোবা কোবি করে দেখছেন কেউ সবাই তামসা দেখে কেউ ফিরায় বা ধরেনা ভয়ভাবে আমাকে কোব দিতে পারে এই ভয়েমিন্নি ডরভয় না করে যে সাহশের সাথে এতো লোকের মজেও দায়ের মুখে ফিরাবার জন্য জান প্রাণ দিয়ে চেষ্টা করছে কিন্ত পারেনাই কি করে সম্ভপ এতো লোক ছিল কেউতো সাহস করে আসেনাই একা মিন্নি কয়জনকে ধরবে যতটুকু করেছে যতেষ্ঠ করেছে যারা বলে অন্য কিছু বলে তারা মানুষ নামে পশ মিন্নির জয় একদিন হবেই হবে দয়া করে মিন্নিকে নিয়ে আর বাজে কথা কেউ বলবেন না না না,0,"Meme, TikTok and others"
দেখি চৈতালি তোমার গুদ টা দেখি হিন্দু মুসলিম দাঙ্গা বাঁধতে চাষ ফেক খবর পাস কোথায় চ্যানেল বন্ধ কর,0,"Meme, TikTok and others"
এইটাকে বন্ধু বলেনা এইটাকে বলে ফাউ খাচে সাকিব সামি হিসেবে সাকিব ওযগু,0,"Meme, TikTok and others"
কমা করা যায় না,0,"Meme, TikTok and others"
কাশ্মীরের স্বাধীনতা চাই ইনশাল্লাহ,0,"Meme, TikTok and others"
নাজামো,0,"Meme, TikTok and others"
মাঘি রা বেশি বুদ্ধিমান,0,"Meme, TikTok and others"
আল্লাহ আপনি আপনার ঘর হেফাজত করুন,0,"Meme, TikTok and others"
লাক্স — বিশ্ব সুন্দরী বাঁধন,0,"Meme, TikTok and others"
তুই তো ফ্রী দিয়েছিস আমাকে,0,"Meme, TikTok and others"
ওকে ফাসি দিয়ে মারা দরকার,0,"Meme, TikTok and others"
বাবরি মসজিদ থাকবে,0,"Meme, TikTok and others"
সানাই তুমি দেখো তোমার তলা ভাড়া দিয়ে সাইজ বড় করছো আর ময়ুরী এমনি এমনি বড় করছে তোমার নিচ তলাও গেছে লাখ টাকাও গেছে ময়ুরী কে যদি আগে থেকে ফলো করতে তাহলে টাকাও থাকতো আর নিচের মেশিনও টাটকা থাকতো,0,"Meme, TikTok and others"
সেই চিলো একটা বাঘের বাচ্ছা বাঘ,0,"Meme, TikTok and others"
যেখানে অন্যয় সে খানে এই রকম প্রতিবাদি লোক দরকার সাবাস,0,"Meme, TikTok and others"
উচিত মত সাচতি দিন কুলাংগারকে,0,"Meme, TikTok and others"
জয় গুরু,0,"Meme, TikTok and others"
হায় আল্লাহ এটা আমি কি দেখলাম,0,"Meme, TikTok and others"
আমি ও চাই সাকিব খান অপু দিদি কাছে ফিরে আসুক,0,"Meme, TikTok and others"
আল্লাহ যেনো তোকে তোর ছেলে কে দিয়ে মার না খাওয়ায় তোর মতো ছেলে ধ্বংস হবে,0,"Meme, TikTok and others"
অাহা মিল্ক ভিটার কথা মনে পড়ে গেল,0,"Meme, TikTok and others"
মিথ্যা প্রচার করতেছেন নয়ন এর থেকে কত টাকা পাইছেন,0,"Meme, TikTok and others"
ইয়ারপুট কাদের টাকায় চলে প্রবাসিদের টাকায় চলে আর ওইকানে কাজকরে গুজখুর পুলিশেরা আর আমাদেরকে বলিস বালের কামলা সালার বেটারা,0,"Meme, TikTok and others"
সিলভার সেলিম ও তার সেক্স ভিডিও দেখে বুঝাযায় সে কি রিলেশনশিপ পছন্দ করেন,0,"Meme, TikTok and others"
ধুর এটা কোন খবর নাএডিট করা আছেখবরটা উনি বলছেন না কম্পিউটার এডিটিং করা,0,"Meme, TikTok and others"
মোদি সরকার বারতের কলঃক,0,"Meme, TikTok and others"
আমি শাকিব আর অপু আপ্পিকে আবার একসাথে মুভিতে দেখতে চাই আর তাদের সাজানো সংসার চাই আর কিছু চাই না,0,"Meme, TikTok and others"
ইনশাআল্লাহ কাশমিরের বিজয় হবে,0,"Meme, TikTok and others"
ভাই এর জন্য ভালোবাসা অবিরাম,0,"Meme, TikTok and others"
এর ভাষা হারিয়ে ফেলেছি,0,"Meme, TikTok and others"
তমার সাতর কি কথা বলতি পারি নবার,0,"Meme, TikTok and others"
ওতিন্দ্রাদা একদম ভালমানুস এক মত হলে লাইক করুন,0,"Meme, TikTok and others"
অবশ্যই চাই কাশ্মীর স্বাধীন হউক ভারত বা পাকিস্তানের প্রদেশ নয়,0,"Meme, TikTok and others"
হুমম দুধ,0,"Meme, TikTok and others"
কাশ্মীর স্বাধীনতা চাই,0,"Meme, TikTok and others"
অাল্লাহ তুমি এর বিচার করআমিন,0,"Meme, TikTok and others"
ওরে আমার কাছে নিয়ায় ওর হাত দুইটা কাইটা কুত্তারে খাওয়াইয়া দিমু,0,"Meme, TikTok and others"
আমরাই পারি এরকম আরাচোদা নায়ক নায়িকা আনতে পারে,0,"Meme, TikTok and others"
মোদির ফাসী চাই,0,"Meme, TikTok and others"
রাইট চাচা,0,"Meme, TikTok and others"
মারতে মারতে নিয়ে যাওয়া উচিত ছিল,0,"Meme, TikTok and others"
মুল বিষয় আড়াল করার জন্য এবং গোপন কোন তথ্য প্রকাশ পাবার ভয়ে মামলাটি অন্য দিকে প্রভাবিত করার চেষ্টা করছেন,0,"Meme, TikTok and others"
ও হ্লা বাপ্পি কুমিল্লার ইতর,0,"Meme, TikTok and others"
পারবে,0,"Meme, TikTok and others"
আমারহবে,0,"Meme, TikTok and others"
আমিও চাই যেনো ওনারা আগের মতোই চলেন,0,"Meme, TikTok and others"
এখন তো ওর মা অনেক টাকা চোখে দেখেছে তাই ওই মেয়েটা মার টাকার দিকে নজর করেছে ওই মেয়েটা কে জুতা পিটা করা দরকার আপনারা কি বলেন যখন ওর মা ভিক্ষা করতো তখন কই ছিল ওই মাইয়া ওই মেয়েকে আমি যদি পাইতাম গামে ছয়টা থাপ্পর দিতাম,0,"Meme, TikTok and others"
লাথি মারা উচিত এইসব সন্তান দের,0,"Meme, TikTok and others"
শাকিব খান তুমি ছেলে আব্রাহাম খান জয় কে বাড়ী গাড়ী টাকা পয়সা ধোন দৌলদ সব দিতে পার বা বাট মায়ের যে অভাব সে টা কোটি টাকা দিয়াও পুরণ করতে পারবা না সে কষ্ট তুমি পাবে শাকিব খান সে দিন তোমার বুক পাটবে বাট মুখ পাটবে না,0,"Meme, TikTok and others"
ফেইসবুকের পোস্ট রিডিং পড়তেছে পোস্ট এর লিখা কপি করে ভিডিও বানাইছে,0,"Meme, TikTok and others"
সবাই মিলে জুতা পিটা করা উচিৎআল্লাহ তুমি সব বাবা মাকে হেফাজত করোএসব জালিম সন্তানদের কাছ থেকে রক্ষা করোআমিন,0,"Meme, TikTok and others"
তুই যা করেছিস তার কোন খমা নাই শুধুই শাস্তি চাই,0,"Meme, TikTok and others"
আচ্ছা এই বাল গুলার কি কোনো মা বাবা নাই🤔🤔🤔🤔,0,"Meme, TikTok and others"
সুপ্রিম কোর্ট সম্পূর্ণ স্বাধীন এবং কারো দ্বারা পরিচালিত নয় ভারতবর্ষের স্বাধীন ভারতবর্ষের এটাই সর্বোচ্চ বিচারালয় এখানে কোন প্রধান বিচারপতি রাজনৈতিক ব্যক্তিত্ব দারা বা রাজনীতির কবলে পড়ে তার সিদ্ধান্ত নির্দেশ করেন না তিনি সম্পূর্ণ সম্পূর্ণ একজন শ্রেষ্ঠ প্রধান বিচারপতি সুপ্রিম কোর্টের বিচারপতি সম্পূর্ণ তথ্য এবং যুক্তি এবং সামান্য বিষয় নিয়েই এই রায় দেয়া হয়েছে এই রায়কে আমাদের সমস্ত ভারতবাসীর এবং সারা বিশ্বের যারা আছেন সকলকে মেনে নেয়া উচিত এবং এনার রায় কে মানতা দেয়া উচিত বলে আমি মনে করি সকলের মঙ্গল কামনা বিশ্বশান্তি বার্তায় পাখি 🦜🦜 পাখি 🦜🦜 হেমন্ত পাইন বন্দি পুর ময়াল বন্দি পুর খানাকুল আরামবাগ হুগলি পশ্চিমবঙ্গ ভারতবর্ষ,0,"Meme, TikTok and others"
আল্লাহ হেদায়েত করোকেয়ামত নিকটে জানোয়ার আজকে বাপরে মারছে কাল তোর সন্তান তোরে মারবোভিডিও টা পুলিশের কাছে দাওয়া উচিত,0,"Meme, TikTok and others"
এই বাবরি মসজিদ রক্ষায় আমার চাচ্চু _ যুগ আগে শহীদ হয়েছে তিনি একজন হাফেজ ছিলেন,0,"Meme, TikTok and others"
ভাইয়া,0,"Meme, TikTok and others"
আখি আপা আপনার অনেক গন্ধ,0,"Meme, TikTok and others"
মিথ্যেবাদী বক্তা আর যত ছাগল ভ্যা ভ্যা করে তাকে বাহবা দিচ্ছে এরা সব মুর্খের স্বর্গে বাস করে আর অলীক স্বপ্ন দেখে,0,"Meme, TikTok and others"
সমাজ আজ কত নিচে নেমে গেছে,0,"Meme, TikTok and others"
ছেলেটাকে পিটানোর দরকার আশে পাশের মানুষের চোখে দেখেনা তারে জুতা পিটা করার দরকার,0,"Meme, TikTok and others"
সরকারের কাছে আবেদন লোক টাকে আইনে মাধমে শাসতি দিবেন,0,"Meme, TikTok and others"
এই সব বাদদিয়ে একটা ভালো হাসপাতাল বা কলেজ করা হক,0,"Meme, TikTok and others"
আমি তোমার কাছে আসব তোমার নামবার থেকে কল দাও,0,"Meme, TikTok and others"
যে জাকের নায়েক সম্পর্কে খারাপ মন্তব্য করবে সে সঠিক মায়ের সন্তান নয়,0,"Meme, TikTok and others"
তোমাদের ভিডিও গুলা ঠিক হয় না মাঝে মাঝে মাঝে মাঝে আমার কথা আর কাজে মিল নেই,0,"Meme, TikTok and others"
স্বাধীনতাগামী কাশ্মীরের পক্ষে,0,"Meme, TikTok and others"
এই মিয়া আপনার আপনার খেয়েদেয়ে কোন কাজ নাই আপনি এত আলতু ফালতু ভিডিও বানান কা আপনার একটা খারাপ মেয়ে ভালো একটা ধোন দেখলো ভিডিও বানাবেন খেয়েদেয়ে আর কোন কাজ আছে পাহাড়ের মাটি কাটার অভদ্রলোক,0,"Meme, TikTok and others"
অতীন্দ্র দা অনেক ভালো একটা কথা বলছে,0,"Meme, TikTok and others"
বিশ্বাস করেন আমি যুদি এমন অবস্থা দেখতাম কেমেরা না করে বডি দিয়ে মাথা কেটে জেলে যাইতাম,0,"Meme, TikTok and others"
কাশ্মীরকে ভালবাস,0,"Meme, TikTok and others"
আমি বিপক্ষে সব মানুষ কে সমান অধিকার দিতে হবে,0,"Meme, TikTok and others"
মুদি কে আল্লাহ দুনিয়া থেকে তুলেনিন এ সব জাতির ধর্মের উপর ওত্রাচার হছ্যে🦁 আমি মানিনা,0,"Meme, TikTok and others"
কাশমীরকে অবশ্যই সমর্থন করবো,0,"Meme, TikTok and others"
টিপাটিপি কম করলেই তো হয়,0,"Meme, TikTok and others"
শাবনূর সর্ব গুনের অধিকারী মোটা হলেও সব সময় দেখতে চাই ওকে,0,"Meme, TikTok and others"
জবার মারে চুদি,0,"Meme, TikTok and others"
এইটা নিশ্চই কোলকাতার যানোয়ার ওকে দিনের রিমান্ড দেয়া হোক ব্রদার,0,"Meme, TikTok and others"
বাল তুলছিস তুইনিজেকে আবাল ছাড়া র কিছু ভাবতে জাস না,0,"Meme, TikTok and others"
মানবিক অধিকার মানুষ হয়ে খুনিদের মত আচরণ হচ্ছে কাশমিরেদের উপর,0,"Meme, TikTok and others"
সাকিবকে আমরা এই ঈদে চাইনা জিতকে চাই,0,"Meme, TikTok and others"
মেদির ফাঁসি চাই,0,"Meme, TikTok and others"
পূণিমা আমার ছোট বেলার ক্রাশ ❤❤❤,0,"Meme, TikTok and others"
আইনের আওতায় আনা হােক,0,"Meme, TikTok and others"
মিন্ন নিদোষ,0,"Meme, TikTok and others"
সিলেটের কুনু তুলুনা হয়না,0,"Meme, TikTok and others"
আপনারা কেন মেয়েটার দোষ দিচ্ছেন মেয়ে টা চাইলে গোপনে মারতে পারত কেউ জানত না আসেন আমরা নয়নের এমন সাস্তি দাবি করি যে এই রকমের অন্নাই কেউ করার শা্হস না পাই নয়ন বন্ড এক দিনে হই নাই আকাম করতে করতেই হইসে আর এখানে প্রসাসনও দাই তারাই তাকে এই রকম সাহস দিচে,0,"Meme, TikTok and others"
আবরার হত্যা মানুষ ভুলে নাই খুন হওয়ার ভয় আছে ভেবেই কেউ এই প্রস্তাবের মতামত দিবে না,0,"Meme, TikTok and others"
আল্লাহ মানুষ এতোটা খারাপ কি করে হয় ছি ছি এই জানোয়ার টা কে এখনো এলাকা বাসি বাঁচায় রাখছে কেনোকুত্তার টাকে হাত পা বঁধে প্রতিদিন খুনতি গরম করে ছেঁকা দেওয়া উচিৎ এর বউটা কেওমাগি দাঁড়িয়ে দাঁড়িয়ে দেখতেছিলযেই হাত দিয়ে ওর বাবার গালে চড় গুলো মারছে সেই হাত পুরিয়ে ফেলা হউকতারপর ফাঁসি দেয়া হউক,0,"Meme, TikTok and others"
শে একজন হাশীর মানুশ সিলো আল্লা তাকে ভেহেস্তো নৌসিব করুক,0,"Meme, TikTok and others"
তোমার কুমিল্লার মেয়েরা কেমন বল্লানা কেন,0,"Meme, TikTok and others"
আমার সয্য হলো না,0,"Meme, TikTok and others"
অপু সামির কথা মানে না,0,"Meme, TikTok and others"
ও আল্লাহ কাওকে এমন সন্তান দিও না আর লিখতে পারলাম না কিছু,0,"Meme, TikTok and others"
জকির সুধু মুসলিমদের জন্য নায়ক কিন্তু আন্যসকলের জ্যন্য খলনায়ক,0,"Meme, TikTok and others"
ভিডিওটি দেখে আমার কান্না পেয়ে গেছে,0,"Meme, TikTok and others"
অপু আপু তুমি সাকিব সাতে চবি কর ভালা লাগবে,0,"Meme, TikTok and others"
বালারশাকিব খান,0,"Meme, TikTok and others"
আমি মালয়েশিয়ায় আচি এবং আমি কাশ্মি পাশেই থাকবো,0,"Meme, TikTok and others"
রানু দিদি কে তার জায়গায় পাঠিয়ে দিন এক দম বেকার,0,"Meme, TikTok and others"
বাবরি মসজিদ ভাঙার শব্দ হল বিশ্বের মূসলমান ধঙ্গস করা জেনে রাকবেন,0,"Meme, TikTok and others"
বিসা চাই,0,"Meme, TikTok and others"
সরকারের কাছে আমার দাবি এ জালিমের বিচার করার জন্য আল্লা তুমি এই জালিমের বিচার কর,0,"Meme, TikTok and others"
চালা লুচু বাপ্পি,0,"Meme, TikTok and others"
আল্লাহতাদের যেন দুনিয়ায় যা করেছে তার উপর হাশর যেন হয়,0,"Meme, TikTok and others"
এই সব কিছুর জ্ন্য দায়ী এক মাত্র শাকিব শাকিবের যদি চরিত্র ঠিক থাকতো তাহলে ওর বউ ও ভালো হতো,0,"Meme, TikTok and others"
মনে হচ্ছে না বলে,0,"Meme, TikTok and others"
মুদির ফাসি হুক,0,"Meme, TikTok and others"
অপুর সাথে যা করেছে সাকিব এটা তার পাওনা ছিলো অপুতো আফসোস করছে আমি হলে খুশি হতাম,0,"Meme, TikTok and others"
সুপ্রিম কোর্টের রায় সঠিক নয়,0,"Meme, TikTok and others"
ও আল্লাহ আমি চোখের পানি আটকে রাখতে পারলাম না ইসস কত খারাপ এমন কেউ করে,0,"Meme, TikTok and others"
বাবরী মসজিদ হিন্দু ধর্ম মতে ভান্গা ঠিক হয়নি যা মুসলমান ধর্মে আঘাত হানে,0,"Meme, TikTok and others"
ভাই ও কে পুলিশে দেন,0,"Meme, TikTok and others"
তরে আমি গোয়াইম,0,"Meme, TikTok and others"
রানু মন্ডল আগে গান গাইত রানাঘাট স্টেশনে এখন ওর মেয়ের বাড়াবাড়ির জন্য পরবর্তীকালে গান গাইতে হবে শিয়ালদার স্টেশন নিজের মেয়ে মাকে পথ দেখাবে কিনা শয়তানের মতন উঠে পড়ে লেগেছে গাঁড় মারবে বলে শয়তান কাকে বলে সাথী কে দেখলে বুঝা যাই যে শয়তান কেমন হয়,0,"Meme, TikTok and others"
বিপক্কে,0,"Meme, TikTok and others"
এরকম বৃদ্ধা বাবা কেহ মারিও না আমার পিতামাতা নেই বলে আমার দুই চোখে জল আসে আর অন্তর কাদে,0,"Meme, TikTok and others"
হাটাও দেশ বাচাও,0,"Meme, TikTok and others"
জনগণ সোচ্চার থাকলে এসব জঘন্য অপরাধের মূল উপড়ে ফেলা সম্ভব,0,"Meme, TikTok and others"
সৌদি আরব ইরানের একটা প্রশ্ন ছিঁড়তে পারবে না শুধুমাত্র মুখে বলে ইরানকে ধ্বংস করতে নাকি আধঘন্টা সময় লাগবে আমি সৌদি আরব কে বলব নিন আধঘণ্টার আপনার ঘন্টা বলেছেন ঘন্টায় তাদেরকে ধ্বংস করে দেখেন পারেন কিনা শুধু মুখে বললে হবে না কাজে কর্মে দেখাতে হবে কারণ সে সত্যিই আপনাদের নেই কারণ আপনারা নিজেই ধ্বংস হয়ে গেছেন অন্যজনকে কি ধ্বংস করবেন অন্য দেশকে ধ্বংস করবেন আপনি নিজেই ধ্বংস নিজেরা বিপর্যস্ত,0,"Meme, TikTok and others"
শাকিব খান ও অপুর জুটি চাই,0,"Meme, TikTok and others"
সৃষ্টির সেরা জীব মানুষ তেমনি সৃষ্টির নিকৃষ্ট জীব ও মানুষ তাই তো মানুষ আজ মানুষকে মারতে দ্বিধাবোধ করে না,0,"Meme, TikTok and others"
আশা করছি হাত এক হবে,0,"Meme, TikTok and others"
এমন পুত্র বেচে রাখার চেয়ে মেরে ফেলা উচিত,0,"Meme, TikTok and others"
কাসমীরি দের বিরুদ্ধে কথা বললেই তাদের মুনডি কেটে নিবো,0,"Meme, TikTok and others"
ডাঃ জাকির নায়েক এর সকল ইসলামী কাজ চালু করে দেওয়া হোক আমিন,0,"Meme, TikTok and others"
ওর খমা গু খাওয়া,0,"Meme, TikTok and others"
তুমার জাহান নাম এর কিং আল্লাহ হিদায়েদ কুরুক সাথে তুমারেও হিপাজত করুক,0,"Meme, TikTok and others"
কে বলছি হেড লাইন এর সাথে কথার মিল নাই কেন,0,"Meme, TikTok and others"
আল্লাতুমি চিনের মুসলিম দেরকে হেফাজত করুন আমিন,0,"Meme, TikTok and others"
আমার এ ইমুতে কল দাও আপু,0,"Meme, TikTok and others"
দিদিকে দেখতে চাই,0,"Meme, TikTok and others"
আমাদের দেশে চামচিকার বাচ্চারা যে বলে এটা নকল সিনামাদরলাম নকল সিনামা তবে যেটা আসল সিনামা সেট কোন চামচিকার বাচ্চারা দেখেছেবাট আসল সিনামার যে ভাষা সেটা কে বুজেছেযারা এই গোলা নিয়ে শাকিবের পিছু নিয়েছেআমার মনে হয় তাদের চৌদ্দু গুষিটও তো আসল সিনামার ভাষা বুজেনা তাহলে আমাদের কিছু কিছু ভাই আছে তারা কেনো উদের কথায় লাফালাফি করে,0,"Meme, TikTok and others"
রানুর গান ফ্যলো হূক,0,"Meme, TikTok and others"
নজর,0,"Meme, TikTok and others"
ত,0,"Meme, TikTok and others"
জাকির নায়েক খুব ভালো মানুষ,0,"Meme, TikTok and others"
ইমরানের পক্ষে,0,"Meme, TikTok and others"
আল্লাহ্ না করুক এমন সন্তান আর কারো হোক,0,"Meme, TikTok and others"
আল্লাহর বিচার দিরে দিরে হবে,0,"Meme, TikTok and others"
জাকের নায়েক একজন খাটি মুসলিম ও আল্লাহর প্রিয় বান্দা আমি তার মঙ্গল কামনা করি,0,"Meme, TikTok and others"
শরীর টা তো দেখ গরুর মতো করছছ,0,"Meme, TikTok and others"
হাওয়া ইচিত,0,"Meme, TikTok and others"
উনার নিজের স্তন তো দেখি ঝুলে গেছে,0,"Meme, TikTok and others"
গোবর,0,"Meme, TikTok and others"
তাই শেষ কথা বলে যাই পাকিস্তান জিন্দাবাদ আজাদ কাশ্মীর জিন্দাবাদ হিন্দুস্তান পুরোপুরি মুর্দাবাদ মুর্দাবাদ মুর্দাবাদ পাশাপাশি হিন্দুস্তান নিপাত যাক নিপাত যাক নিপাত যাক,0,"Meme, TikTok and others"
মুক্তিযোদ্ধাঢাকা বিশ্ববিদ্যালয়ের প্রফেসর,0,"Meme, TikTok and others"
হায় রে মানুষ,0,"Meme, TikTok and others"
ওরটা করো না কেন,0,"Meme, TikTok and others"
ওর হাত পা বেধে পেটানো উচিত,0,"Meme, TikTok and others"
খালি বিচার চাই বলছ সবাই বিচার অার কবে হবে সৌদিঅারব প্রভাসি দেলওয়ার,0,"Meme, TikTok and others"
রানু মণ্ডলের অপব্যবহারের জন্য আজকে খীপত হয়েছে এই যে অহংকার তাকে এক দিন যে যায়গায় ছিলেন তাকে সেই জায়গা য় চলে যাওয়া উচিত কারণ তিনি যে অতীত মতো মানুষ কে এই ভাবে অপমান করার তাঁর কোন অধিকার নেইরানু মণ্ডল কে এই যায় গা থেকে পাঠানো দরকার তার আমরা অনেক কথা শূনছি কিন্তু তিনি জেনে বুঝে কথাটি বলেছেন রানু মণ্ডল,0,"Meme, TikTok and others"
মূর্খ উপস্হাপক,0,"Meme, TikTok and others"
কাসমির,0,"Meme, TikTok and others"
ইউটুবে অনেক বেড়ে যাচ্ছে থামলাইন এর সাথে মিল নাই তাই আনসাব করে দিলাম,0,"Meme, TikTok and others"
তুই আসবি নাকি,0,"Meme, TikTok and others"
আমরা পাকিস্তান,0,"Meme, TikTok and others"
আল্লা সকল মানব জাতিরে মানবের মত চলার তহপিক দেন আল্লা আমিন,0,"Meme, TikTok and others"
মিন্নির ব্যাগ খুনি দের হাতে কেনোকেন মিন্নিকে একটি আগাত ও করলোনা কেনো মিন্নি রিফাত কে ধরলোনা,0,"Meme, TikTok and others"
সাখা চৌধুরি একজনি তার কোনো জোড়া নেই সে আমার খুন পছন্দের নেতা,0,"Meme, TikTok and others"
ও কি মানুষ,0,"Meme, TikTok and others"
রিয়াজ পূজা করতে গেছে বাগেরহাট সিকদার বাড়ী অপু কে নিয়া যায় নাই সাকিব তো বুবলিকে নিয়া বিজি,0,"Meme, TikTok and others"
আমার গার্ল ফ্রেন্ডের এসথন ঝুলে গেছে এখন কি করতে পারি আমি,0,"Meme, TikTok and others"
মৃত মানুষ আর নামাজ নিয়ে কতা বলবি না,0,"Meme, TikTok and others"
আমি চাই তিনজন এক সাথে সারা বছর থাকতে,0,"Meme, TikTok and others"
ওহ্ এই মিত্থাবাদিটা,0,"Meme, TikTok and others"
নয়নের ও মন্নি ফাঁসি চাই,0,"Meme, TikTok and others"
পাকিস্তানের জই হবেই ইনশাল্লাহ,0,"Meme, TikTok and others"
খুবতো গুছিয়ে বলতে পারেন,0,"Meme, TikTok and others"
আমরা চাই এক হয়ে যাকআবার তারা জুটি বাদুক,0,"Meme, TikTok and others"
এই কাপুরুষ কে তো উল্টো ঝুলিয়ে পেটানো দরকার,0,"Meme, TikTok and others"
সাকিবকে বাদ দিলে অপুকেও বাদ দিতে হবে অপু একটা সয়তান মহিলা ছবিতে কি বাবে আসছে ও যানে ও আর ছবি করতে পারবেনা মোটা হয়েছেটাকা খাওয়ার জন্নো সাকিবের নামে বদনাম বলে বউ বউ নাটক করেছে নায়িকারা ভালো হতে পারেনা কারন যেই ড্রেচপরে আর নায়োকের সাথে ডলাডলি করে তাতে ভালো প্রশ্নই আসেনা তার উপর বিয়ার আগে বাচ্চা দর্সোক কি জন্নো অপুর পক্ষনেয় বুজতে পারিনা সাকিবকে ফাসানোর জন্নো মানুষের বুদ্দিতে টিবির সামনে এসে কেদে কেটে এই কাজ করেছেসাকিবের পিছনে সত্রুতা করতেছে সালমান সাহ মতো বাংলাদেশে এই একটা সমোস্সা কেউ বড় হইলে তাকে মেরে ফেলা হয় সাকিবকে বহিস্কার করলে ইনডিয়ায় যাইয়া ছবি করবে বাংলাদেশের জন্নো খারাপ এমনেতেই এফডিসি ভারতের দখলে তার উপরে ভাল নায়োক বহিস্কার,0,"Meme, TikTok and others"
আল্লাহ এমন ছেলে কাউকে দিওনা,0,"Meme, TikTok and others"
তোমার নাবার দেও বিয়ে করবো সব জেনে তোমার টাকা লাগবো আমি দেবো পিছ আমার ইমো,0,"Meme, TikTok and others"
মনে রাখবে একজন উপোর ওলা আছে উপোর ওলারে ভুলে জেওনা,0,"Meme, TikTok and others"
খুব ভাল এগিয়ে যাও অপু,0,"Meme, TikTok and others"
অপু আর হিরো আলম কে দেখতে চাই এক মুভিতে,0,"Meme, TikTok and others"
দেশে ফিরা থিক হবে না,0,"Meme, TikTok and others"
একটা কথা ভালো করে বুঝলাম যত বড়ো জাতের মানুষ তাঁদের মন মানসিকতা ততো উন্নত যেমন মুখার্জী চ্যাটার্জী ভট্টাচার্য এনারা কত সুন্দর বোঝে এনারা জানেন সবার ওপরে মানুষ সত্য নিয়ে কত সমস্যা মানুষ আর কত কষ্ট সেটা কিন্তু যারা সত্যি অন্য কাস্ট র তারা শুধু মুসলিম দের কষ্ট পাবে বলে অনেক খুশি,0,"Meme, TikTok and others"
সিয়াম,0,"Meme, TikTok and others"
শাকিব তো বুবলী কে নিয়ে বেসতো তাহলা জয়ের কথা কখন সে ভাবে যত সব ফালতু কথা,0,"Meme, TikTok and others"
আপনি মেয়ে হয়ে কি ভাবে এগুলো বলেন ছি ছি আপনাকে জুতা পিটিয়ে সজা করা দরকার,0,"Meme, TikTok and others"
বাংলাদেশের সানিলিওন,0,"Meme, TikTok and others"
চা বিক্রি করে করে করে মারামারি ঝগড়া হিংসা ছাড়া কিছুই শিখেনি মূখ্ মদি,0,"Meme, TikTok and others"
জাকির নায়েক ভারতে যায়া ঠিক হবেনা ওরা অত্তা চারি,0,"Meme, TikTok and others"
ওকে,0,"Meme, TikTok and others"
যখন মারছিলো কেউ কি ওখানে ছিল না না সবাই দেখে মজা নিচ্ছিল,0,"Meme, TikTok and others"
ওরনায় ও ধরায় না এতো বড়,0,"Meme, TikTok and others"
এতে আমি একমত,0,"Meme, TikTok and others"
পাকিস্নন জয় হক আমিনমুসলমান জয় হোক মুসলমানদেরকে আল্লাহ তুমি হেফাজত করো কাশ্মীরের স্বাধীনতা চাই মোদির ফাঁসি চাই,0,"Meme, TikTok and others"
রানু একটা বেইমান অহংকারী মহিলা ওকে নামিয়ে দেওয়া ঠিক,0,"Meme, TikTok and others"
তুই একি করলিরে,0,"Meme, TikTok and others"
ধূর বৎসর গুনা ঠিক কর,0,"Meme, TikTok and others"
এইসব মিথ্যা কথা ভয়েস বন্ধ করে অন্য কেওবলছেন খবর,0,"Meme, TikTok and others"
ভাই এসব কথা ভালো না আপনে কি মানুষ না আর কিচো,0,"Meme, TikTok and others"
পিছনের ভাই কেমনে হাসি ছাড়া থাকতে পারে,0,"Meme, TikTok and others"
সানাই দেখ হাতে তৈরি কেমন,0,"Meme, TikTok and others"
তুমার চেয়ে তুমার দুধ সুন্দর,0,"Meme, TikTok and others"
ঠিক করে ছে,0,"Meme, TikTok and others"
আমিতোমারচোদারদিকেইছি,0,"Meme, TikTok and others"
ওর বৌটাকে দরা দরকার,0,"Meme, TikTok and others"
একে ফাসি দিন,0,"Meme, TikTok and others"
পাগ হয়ে গেছে সে নাস্তিক,0,"Meme, TikTok and others"
কাশ্মীরদের পক্ষে আছি থাকবো,0,"Meme, TikTok and others"
ভারতে কোনো মনদির হবেনা,0,"Meme, TikTok and others"
তারা জেন এক হয়ে জাই আললাহ তাদের সঠিক বুজ দান করুক আমিন,0,"Meme, TikTok and others"
ছিলুটি মেয়েরা রুটে গাটে পুটকি মারা দেই,0,"Meme, TikTok and others"
এইটা আমার নম্বার,0,"Meme, TikTok and others"
ম,0,"Meme, TikTok and others"
বাবরি মসজিদ ছিল থাকবে,0,"Meme, TikTok and others"
ওই সাথি এত দীন কেথাই ছিল যে মা ভালো হয়েছে তাকে খাবে,0,"Meme, TikTok and others"
আপনার সাথে নোংরা কাজ করেছে জানেন কিভাবে জীবনে উড়োজাহাজে চড়েছেন,0,"Meme, TikTok and others"
পিছা মারি তোর কপালে,0,"Meme, TikTok and others"
কাশ্মীর কলিকাতা দুইটাই স্বাধীন হওয়া উচিত তাহলে ভারতের জন্য মঙ্গল হবে আমি মনে করি,0,"Meme, TikTok and others"
অামৱা চাই সাকিব অপু অাবাৱো জুটি বেধে ছবি কৱোক,0,"Meme, TikTok and others"
কোনো মাফ হবেনা এটাকে ফাশি দিতে হবেপ্রতিটা চড় যেনো আমার কলিজাই লাগছে এটা কি মানুষ,0,"Meme, TikTok and others"
আলটিমেটলি ভারতের কপালে মারত্মক শনি আছে,0,"Meme, TikTok and others"
আমি মোদির কে বিশ নেতা বানাতেচযায়,0,"Meme, TikTok and others"
অনেক বালো,0,"Meme, TikTok and others"
এটা ক্ষমার যোগ্য না,0,"Meme, TikTok and others"
সে কিভাবে হাসি ছাড়া দাড়িয়ে আছে 🤣,0,"Meme, TikTok and others"
আন্টির সোনা কালা হাহাহা,0,"Meme, TikTok and others"
শাকিব খান তোমাকেই বলছি তোমাকে ছাড়া অপু অনেক ভালো আছে অনেক ভালো থাকবে,0,"Meme, TikTok and others"
শুধূ কাশ্মীর নয় আর ও কিছু স্বাধীন হবে কারন যে ভাবে গোরক্ষা লাভ জিহাদ মব লিচিং মুসলিম অবমাননা বিদ্বেষ ছড়ানো হচ্ছে আর্থিক ভাবে দুর্বল হচ্ছে তাতে বেশি দূরে নয়,0,"Meme, TikTok and others"
দয়া করে আমার চ্যানেল টি করুনলাইক দিনআপনার চ্যানেলকে করতেছি,0,"Meme, TikTok and others"
জায় হিন্দ্দ,0,"Meme, TikTok and others"
রানুদিএকটি ধকাবাজ,0,"Meme, TikTok and others"
আমার মতে সাকিব ও অপু এক হয়ে গেলে অনেক সুন্দর লাগবে,0,"Meme, TikTok and others"
বকাবকি না করাই ভালো পারলে কাজে প্রমাণ করুন,0,"Meme, TikTok and others"
পাকিন্তান জিতবে,0,"Meme, TikTok and others"
সর্তী বলছি ভিডিও টা দেখতে পারছি না,0,"Meme, TikTok and others"
কুকুর কুকুরি থাকে,0,"Meme, TikTok and others"
পাকিচ থান,0,"Meme, TikTok and others"
ইসলাম,0,"Meme, TikTok and others"
যাদের কোনো অভিজ্ঞতা নেই এই মানুষরা কেনো শরনার্থী হলো এমন সব তথাকথিত বিরোধী যে সব মন্তব্য বা বিরোধিতা করছে তাদের এ বিষয়ে কোনো বাস্তব অভিজ্ঞতা নাই তাই এরা এসব সেকুলার মন্তব্য করে নিজেদের গর্বিত মনে করছেন আসলে বপনারাতো সাফার করেননি তাই ঠান্ডা ঘরে বসে সহজেই সব মন্তব্য করা সামান্য কিছু নিপীড়িত মানুষের নাগরিকত্ব কে আটকাতে সারাবিশ্বের মুসলমানদের ক্ষেপিয়ে তুলছে ভারতের বিরুদ্ধে যায় ফলে হয়তো ভারত কে গ্রাস করার পথ করে দিচ্ছে এরা এবং হিন্দুত্বের সমাধি খুরছে এইসব তথাকথিত সেকুলার হিন্দু বলে দাবি করে এমন জাতশত্রুরা নির্বোধরা দাঁত থাকতে দাঁতের মর্যাদা দিতে যানে না বুঝবি বুঝবি সব হারিয়ে বুঝে কি লাভ তার থেকে শরনার্থীদের মেরে ফেল দেশবিভাগের বলি যতো হিন্দু ঐ উল্লেখিত তিন দেশ থেকে এসেছে তাদের এবং তাদের বংশধর দের মরিচ ঝাঁপি বা জেরুজালেমের মতো সব মেরে ফেল আর বহিরাগত মুসলমানদের নাগরিকত্ব দিয়ে ওদের মতো হয়ে নিজের জাত ধর্ম খু্য়িয়ে ক্ষমতায় থাক আমরা আকাশ থেকে দেখবো তোদের তোরা কি এখনো হিন্দু না মুসলিম,0,"Meme, TikTok and others"
কে কে প্রিয়াঙ্কা চোপড়া র গুদ মাইরে পাঠাইতে চাও,0,"Meme, TikTok and others"
বিপোখে,0,"Meme, TikTok and others"
কেমন হিন্ধু এগুলো মসজিদ ভেঙ্গে মন্দির বানানোর চেষ্টা করেএটা কেমন ধর্মযদি এইরকম ধর্মে লিখা থাকে তাহলে সেইটা কোনো ধৰ্ম নাকি,0,"Meme, TikTok and others"
খুব ভালো লাগলো ধন্যবাদ জানি না যে স্বপ্ন আছে মনে যে একটি গান করবো প্রবাস জীবনে পূরন হবে কী না,0,"Meme, TikTok and others"
পা,0,"Meme, TikTok and others"
ভাই তুমি অপু আপুকে মেনে নাও,0,"Meme, TikTok and others"
মা খাছে,0,"Meme, TikTok and others"
ভাষার প্রকাশ করতে পারছিনা কি বলবো,0,"Meme, TikTok and others"
বাপী কে চলচ্চিত্ৰ যগত থেকে বহিষ্কাৰ কৰা হক ভণ্ড লোক অ তাৰ মাকেও গুৱা মাৰতে পাৰবে,0,"Meme, TikTok and others"
মদি আর শাহা কে পাগলা কুকুর কেটেছে তাই এমন করছে,0,"Meme, TikTok and others"
দেবের একটা মুভি চাদের পাহাড় এই এক ছবির জনপ্রিয়তার কাছে বাপ্পির কোন মুভি হবে কিনা জানিনা,0,"Meme, TikTok and others"
ইয়া আল্লাহ তুমি আমাদের বাবরী মসজিদ রক্ষা করো আমিন,0,"Meme, TikTok and others"
এতে কোনো সন্দেহ নাই যে অচিরেই এদেরও ডিভোর্স হবে,0,"Meme, TikTok and others"
এদের কে বাঁচিয়ে রাখে কেন জনগণসবার আগে কোনো কথা হবে নাউদোম মারমারতে মারতে মেরেফেলো এরকম কুলাঙ্গার দেরপ্রশাসন যতই ধরে নিয়ে শাস্তি দিকএদের কোনো কিছুতেই কিছু হবে নাকুকুরের লেজ এই মতো এদের মানসিকতা ছি ছিছি এরা কেমন করে পারে এগুলো করতে ছি,0,"Meme, TikTok and others"
প্রেম করেপ্রেমে পড়ে কিন্তু প্রেম জমিয়ে করে এটা কেমন ভাষাপ্রেম কি হিমায়িত পণ্য যে জমানো ছাড়া কাজে লাগানো যায় না,0,"Meme, TikTok and others"
ছুদির ভাই মুদি বেশী বেশী গরুর মুত খা ৷,0,"Meme, TikTok and others"
তুমি একটা মুছলিম মেয়ে হয়ে কি করে খোলা মেলা ভাবে ঘুরে বেড়াওতুমি তো জালিয়ের মেয়ে তোমার মত আর খারাপ মেয়ে আর যেন এই পৃথীবীতে না জন্ম না নেয় মারা গেলে তোমাকে আগে জাহান নামে পুরবে বিনা হিসাবে,0,"Meme, TikTok and others"
কর্ম রিটার্ন আসে রে অমানুষ তুই রেডি থাক,0,"Meme, TikTok and others"
কি বলে এসব,0,"Meme, TikTok and others"
আমার খুব কষ্ট লাগছে এই ভিডিও টা দেখে,0,"Meme, TikTok and others"
অপুর মাতায় সিদুর কে,0,"Meme, TikTok and others"
নির্দুষ,0,"Meme, TikTok and others"
বাবরি মসজিদ ভাঙতে দেওয়া হবে না,0,"Meme, TikTok and others"
রহকল,0,"Meme, TikTok and others"
শুদু মসজিদ চাই,0,"Meme, TikTok and others"
শ্রদ্ধেয় বন্ধুগণ আমি মঙ্গলবার অথবা বুধবারে আমাদের চিটাগাং এর অবস্থিত রাউজান এ বৃদ্দাশ্রম যাবো আমার সাথে আমার এক বড় ভাই এবং আমার কয়েকজন বন্ধু যাবে আপনারা কেউ গেলে আমাকে জানায়েন উদ্দেশ্য হল ব্যক্তিগত আমার ইচ্ছা কমপক্ষে এক জনকে হলেও তাদের সন্তানদের ঠিকানা নিয়ে ওদের ছেলে মেয়ে কাছে দিয়ে আসা কেউ গেলে আমাদের জন্য ভালো হয় সবাই দেখা উচিত ওখানে অনেক কিছু শেখার আছে,0,"Meme, TikTok and others"
রাজাকারের বাচ্চা রাজাকার,0,"Meme, TikTok and others"
মুদার ইসলামাবাদ ‌,0,"Meme, TikTok and others"
মিথিলাকে একদিন কাঁদতে হবে তাহসান অনেক ভাল ছেলে,0,"Meme, TikTok and others"
শাকিব অপু আবার বিয়ে হোক,0,"Meme, TikTok and others"
অপুকে,0,"Meme, TikTok and others"
মাননাসেরানায়াকআমাজানসেরামাননা,0,"Meme, TikTok and others"
আমিও করব,0,"Meme, TikTok and others"
ভাই ওরে জবাই কর তা না পারলে বাংলাদেশে পাঠাইদে ওরে সামনে পাইলে যে আমি কি করব জানিনা,0,"Meme, TikTok and others"
একদম ঠিক বলেছেন আপু,0,"Meme, TikTok and others"
শাখিপ সাথে অপু বিশ্বাস জুটি লাগে আমার দের,0,"Meme, TikTok and others"
তুই আমার ঐটা,0,"Meme, TikTok and others"
বাবরি মসজিদ কে ভাংতে দিবনা আমরা৷৷ ৷৷ গরজে উঠ মুসলিম৷ দেখিয়ে দাও মুসলমান কি,0,"Meme, TikTok and others"
জোর করেই জবানবন্দি নেওয়া হয়েছে,0,"Meme, TikTok and others"
জাকির নায়েক বর্তমান যুগের এক জন আদর্শ মানুষতিনি সঠিক পথ প্রদর্শকউনাকে আমাদের অনুসরণ করা উচিত হে আল্লাহ্ আপনি উনাকে রক্ষা করুন,0,"Meme, TikTok and others"
হিনদু হিন্দু কোন জাতি নয়,0,"Meme, TikTok and others"
ওকে সামনে পাইলে ওর বুকের উপর পরোমানবিক বোমা মারতাম,0,"Meme, TikTok and others"
দুধের লিটার কত,0,"Meme, TikTok and others"
হায়রে অভাগা ছেলে,0,"Meme, TikTok and others"
সত্যি বলার মত ভাষা হারিয়ে ফেলছি কি বলবো যত বারি বাবার গায়ে হাত তুলছে তত বারি নিজের অজানতে বুকের বাম পাশে কেপে উঠল,0,"Meme, TikTok and others"
রানুকে আবার রানাঘাট পেছনে রেখে দেওয়া উচিত,0,"Meme, TikTok and others"
কেউ খারাপ কথা বা বাজে কমেন্ট করবেন না সবাই ভদ্রতা বজায় রাখুন,0,"Meme, TikTok and others"
বাংলাদেশ তো দানের দেশ,0,"Meme, TikTok and others"
তোমাকে সবাই বিয়ে করবে তোমি জে হট,0,"Meme, TikTok and others"
ভগভানের ছাকর কারে ভলা হয় ও ঘুলা মানুষকে যেঘুলা মানুষ নিজের সারত ছেড়ে দিয়া ভঘভানের হুুকোমে অন্যের ঝীবন গড়েদে তারে ভলা হয় ভগ ভানের ছাকর অতিনদ্রদা কোভ কোভ ভালা মানষ ভগমান অতিনদ্র দা দা রে জে শাদনা করলে সরগে দেয়া জায় সেই শাদনা করার জগ্যতা ধান করোন আফনারার সভার মতা মত কি ভলুন,0,"Meme, TikTok and others"
শাকিব যাকে দেখে তাকেই ওৰ ভালো লাগে ও একটা খাৰাপ ছেলে অপুৰ মতো এক জন কে অনেক কষ্ট দেই ও কখনো ভালো হবে না,0,"Meme, TikTok and others"
দাদা আপনি খুব ভালো আপনি অন্যের কথায় কান ভার করবেন না কাজ চালিয়ে যানভগবান আপনার মঙ্গল করুক,0,"Meme, TikTok and others"
আপু মনে হয়টকশোর পরে ভাই কে নিয়ালিটন ভাইয়ের ফ্লাটে গেছে,0,"Meme, TikTok and others"
ইন্ডিয়া শুধু মুসলমানদের শত্রু নয় বরং সারা পৃথিবীর শত্রু,0,"Meme, TikTok and others"
আমার ফেভারিট খুব ভালো লাগে অর অভিনয় নায়িকা হিসাবে পারফেক্ট হইবে,0,"Meme, TikTok and others"
পশুর ও অধম,0,"Meme, TikTok and others"
কান্নারাগ খানকিরপোলারে সামনে পাইলে মারতে মারতে মোতাইনা ফেলতাম বেনচুদ আর বাবা বেচারা তারপরেও ছেলে কে বাচানোর চেষ্টা করছে,0,"Meme, TikTok and others"
ইসলাম নিয়ে খারাপ বলবে না,0,"Meme, TikTok and others"
বাংলাদেশের যে সব লোক দেরলজ্জাঘৃন্নাআছে তারা পাকিস্তানের পক্ষ নিবে না,0,"Meme, TikTok and others"
তাহসান হলো বিক্রমপুরের পোলা টাকা তোলা,0,"Meme, TikTok and others"
ডুল গুলো এত বর কেরে,0,"Meme, TikTok and others"
এটা বোখারির কথা সঠিক নয়,0,"Meme, TikTok and others"
অপুর দুধ অনেক বড়,0,"Meme, TikTok and others"
ধন্যবাদ আমরা চাই সাকিব খান অপু খান এক হক অনেক সুন্দর লাগছে ❤,0,"Meme, TikTok and others"
কান্না চলে আসছেএর একটা বিচার করেনযাতে আর কোন ছেলে মা বাবা সাথে এই রকম করতে সাহস না পাইপ্লিজ বিচার করেনআইনের কাছে নিয়ে যান,0,"Meme, TikTok and others"
সেফুদা আমার বস❤,0,"Meme, TikTok and others"
ওহ আল্লাহ্ এই রকম সন্তান কারো হাওয়ার আগে যেন মারা যায়,0,"Meme, TikTok and others"
প্রিয়া শাহার ফাসি চায়,0,"Meme, TikTok and others"
যত সব লুচ্চামি,0,"Meme, TikTok and others"
আর্মি পাকিস্তান আর্মি মুসলিম আওয়ামীলীগ হিন্দু তাই তারা ভারত তাদের জান প্রাণ,0,"Meme, TikTok and others"
এমন কুলাজ্ঞার জত পুলিশ অাছে তাদের সবাইকে বহিসকার সহ শক্ত বিচার করতে হবে,0,"Meme, TikTok and others"
দুনিয়া কেয়ামত হতে দেরি নাই,0,"Meme, TikTok and others"
আল্লাহ মানুষ সহ্য করলেও তুমি কেমনে সহ্য করলা,0,"Meme, TikTok and others"
এখানে জিম্মি পিতা,0,"Meme, TikTok and others"
পায়ের জুতো মাথায় তুলতে নেই,0,"Meme, TikTok and others"
অর হাত পচে যাবে,0,"Meme, TikTok and others"
আমার মনে হয় অপু এখন যে কথা গুলো বলছে ওই কথা গুলি তার মনের কথা নয় কারণ অপু সাকিব খানকে খুব ভালো বাসে,0,"Meme, TikTok and others"
হম সত্যি কথা বলছে,0,"Meme, TikTok and others"
অতিন্দ্র দা যা করেছে রানুদির জন্য তা হয় তো অন্য কেউ করত না তার জন্য ধন্যবাদ,0,"Meme, TikTok and others"
জুতা মার সাকিব কে,0,"Meme, TikTok and others"
মসজিদ এর জায়গায় মসজিদ চাই,0,"Meme, TikTok and others"
প্রত্যেক টা থাপ্পড় কলিজায় লাগছে ওরে পাইলে আনলিমিটেড ইচ্ছা মতো থাপড়াইতাম,0,"Meme, TikTok and others"
রানুকে যেখানে ছিলো টেশনে ছুড়ে ফেলে দে,0,"Meme, TikTok and others"
ডাঃ জাকির নায়েক নির্দোষী,0,"Meme, TikTok and others"
আপু আপনার একরাতের রেট কত জানাবেন তাড়াতাড়ি টাকা মেনেজ করতে হবে তো,0,"Meme, TikTok and others"
এই চেনেলটি ভারত বিরোধী মন্তব্য দিচ্ছে তাইসমগ্র ভারতবাসী এই চেনেল বন্ধ করে দেওয়ার জন্য জেগে উঠোন পাকিস্তান কখনো কাশ্মীরে সফল হতে পারবেনা এটা সত্য জয় হিন্দ জয় ভারতমাতা কী জয়,0,"Meme, TikTok and others"
ভাইয়া আমরা সবাই মিলে আপনার সাথে আছি একে কঠিন থেকে কঠিন শাস্তি দেওয়া ওর গায়ের চামড়া তুলে ফেলুন,0,"Meme, TikTok and others"
ওকে চাকরি চোত করা উচিত বাবার গায়ে হাত,0,"Meme, TikTok and others"
ইমুতে সেকচ করবো ইমু নাম্বার,0,"Meme, TikTok and others"
ওই রকম বাচ্চা কে ওলটো করে খেলাতে হবে,0,"Meme, TikTok and others"
খুব ভালো কাজ,0,"Meme, TikTok and others"
কি ভাবে হাত টা উঠালো হাত টা একটুও কাপলো না হে আল্লাহ,0,"Meme, TikTok and others"
আপু মিথিলা বেপসাও পততা,0,"Meme, TikTok and others"
শাকিব খান সেরসা,0,"Meme, TikTok and others"
তোর উপর আল্লাহর গজব পড়ক,0,"Meme, TikTok and others"
আল্লাহর গজব পডুকযে বাবা মাকে অত্তাচার করেযে ভিডিও করছে এই কুত্তার বাচ্চা বাধা দেয় নাই কেন আগে,0,"Meme, TikTok and others"
স্যার আপনি আমাদের মুখ্যমন্ত্রী মমতা ব্যানার্জী সম্পর্কে একটা ভিডিও বানান,0,"Meme, TikTok and others"
আপু তুমি শুধু বড় সাথে কথা বলে আমার সাতে,0,"Meme, TikTok and others"
অপু ও শাকিব হোক,0,"Meme, TikTok and others"
এত বড় দুধ টিপে মজা নাই,0,"Meme, TikTok and others"
মেসির কোন বিকল্প নেই মেসি একাই ফ্রান্সকে উড়িয়ে দেবে,0,"Meme, TikTok and others"
বোরো বোরো কথা গুলো এতদিন ছিল কথাই,0,"Meme, TikTok and others"
আমি বরাবরের মতোই পাকিস্তান এবং কাশ্মীর পাকিস্তান জিন্দাবাদ অর কাশ্মীর জিন্দাবাদ,0,"Meme, TikTok and others"
মেসি আমার প্রিয়,0,"Meme, TikTok and others"
এগিয়ে যাও বিশ্ব মুসলিম,0,"Meme, TikTok and others"
দুজন আবার একসাথে থাকুক,0,"Meme, TikTok and others"
নিজে না খেয়ে কাদের কে খাইয়েছিলো কার জন্ন্য করেছিলো কস্ট অমানুষ গুলাদের আল্লাহ দুনিয়া থেকে উঠায়া নেয় না কেন ওদের জন্ন্য আজ নিজেদের লজ্জা লাগে,0,"Meme, TikTok and others"
আল্লাহ্ তুমি ওনার বিচার দুনিয়ার মাধ্যে দেখাইয়া দেও,0,"Meme, TikTok and others"
জমিন নিবোনা নিবোনা নিবোনা,0,"Meme, TikTok and others"
মাসআললাহ কল দিন,0,"Meme, TikTok and others"
শাকিব অপুর জুটি চাই,0,"Meme, TikTok and others"
অতীন্দ্র দাদা অনেক ভালো মানুষ অনেক ভালো কাজ করেছে আরও তিন দাদাকে কেনভাস আছো তোমরা তোমরা তোমাদের কে ভগবান কখনো ক্ষমা করবে না তোমরা মনে রেখো কথাটা ভগবান কিন্তু তার সাথে আছে একটা ভগবানের এসেছে,0,"Meme, TikTok and others"
সাকিব তোমাকে বলছি জয়ের কথা চিন্তা করে তুমার ঘরে তুমি পিরে যাও অপো আপোকে মেনে নাও,0,"Meme, TikTok and others"
কাশ্বমির,0,"Meme, TikTok and others"
প্রচারিত খবর যাহা লিখা হবে ওটাকেই রাখবেন কাটাছিড়া করবেন না জাকির নায়েক কে আমেরিকা রাশিয়ার চিনের প্রেসিডেন্ট চেয়েও উপরে নাকি মোদীত ভারতীয়ের নাগরিক একজন প্রধানমন্ত্রী সে মন্দই হোক আর ভালই হোক সে তার দায়িত্ব পালন করিতেছে অন্য একজন অন্য রাষ্ট্র থেকে কিছু বলবে বা করবে আর মোদীকে দোষারূপ করবে সেটা ঠিক নয় সে একা দায়ী নয় সে একজন নির্বাচিত ব্যাক্তি সে একজন চৌকিদার সবার সন্মত মতকে সে প্রকাশ করবে ভারতের গনতনত্র সবার সহমত ও সন্মতগ্রাহ্য বিষয়কে নিয়েই সারাবিশ্বে সে তুলে ধরে প্রকাশ করবে সে একার চিন্তাধারা নিয়ে কখনও মত প্রকাশ করবেনা অন্য রাষ্ট্রের মত একজন সৈন্যের নায়েক দ্বারা জরুরী ভিত্তিক ভারতে শাসনপ্রনালী চলেনা পূর্বের আমার মন্তব্যের কাশ্মী কার শব্দটি কাটা হইয়াছে আর এর পরের শব্দটি ও কাটাছিড়ে দেওয়া হয়েছে আমি যেটি লিখেছি ও মত প্র্কাশ করেছি ওটাকেই দেবেন,0,"Meme, TikTok and others"
আমি চাই কাশ্মীর সাধিন হুখ,0,"Meme, TikTok and others"
কন জাগা,0,"Meme, TikTok and others"
ভারত জিতবে,0,"Meme, TikTok and others"
ভাই গান ভাল ভালো লাগে আজকে থেকে দিন ধরে শুধু তেরিমেরি তেরিমেরি শুনছি এর আগে পিছে কি আর কিছু নাই,0,"Meme, TikTok and others"
শাকিব খান কোন নায়ক নায়ক সালমান শাহ,0,"Meme, TikTok and others"
বাংলাদেশ চলচ্চিত্র উন্নয়ন কাঠামো মেরুদন্ড টা ভেঙ্গে দিয়ে গেছে,0,"Meme, TikTok and others"
সাবনুর এর অভিনয় অনেক দারুন,0,"Meme, TikTok and others"
আললা তুমি এর বিচার করো,0,"Meme, TikTok and others"
অল্প পানির মাছ বেশির পানিতে নামলে বেশি লাফালাফি করে অহংকার মানুষকে পতন করে,0,"Meme, TikTok and others"
অরে মাইরালা,0,"Meme, TikTok and others"
নাউযুবিললাহ আল্লাহ যেনো তাকে হেদায়েত নসিব করেন,0,"Meme, TikTok and others"
নাউজুবিল্লাহ ওয়াস্তাগফিরুল্লাহ হে আল্লাহ তুমি মাফ করআর দেখতে পারলাম না কলিজার কাপন থামাতে পারছিনা আল্লাহগো লেখার জন্য হাত চলছে না বলার মতো ভাষা পাচ্ছি না আল্লাহ আপনি রহম করুনমাবুদ আমাদের সবাইকে আপনি এই পাপ কাজ হতে বিরত রাখুন আল্লাহ আপনি আমাদের হেদায়েত দান করুন আমিন,0,"Meme, TikTok and others"
এর মত নির্লজ্জকে বাঘ এর উপাধি দিয়ে ঠিকই করেছে সবাই মেছোবাঘ ও কিন্তু বাঘ,0,"Meme, TikTok and others"
শালারপুত,0,"Meme, TikTok and others"
ওয়াওওও অনেক সুন্দর,0,"Meme, TikTok and others"
তীব্র বিপক্ষে,0,"Meme, TikTok and others"
আমি ঈশ্বরের কাছে কামনা তার সন্তান যেন তার ওপরে এইরকম পশুর মতো ব্যাবহার করে,0,"Meme, TikTok and others"
আমরা চাই সাকিব অপু আপু কে আবার এক সাথে দেখতে চাই চাই চাই,0,"Meme, TikTok and others"
আল্লাহর কসম করে বলছি তোরে পাইলে গরম ডিম তোর পাচা দিয়া ঢুকাইতাম মাদারচোদ,0,"Meme, TikTok and others"
জুত পিটা করা দরকার,0,"Meme, TikTok and others"
ভারত সরকার ফাসি দিয়ে দিক এটাকে,0,"Meme, TikTok and others"
আমি তোমাকে নাইকা রুপে দেখতে চাই,0,"Meme, TikTok and others"
বাজেকথাই মজানেই পবিত্র সিল্পি,0,"Meme, TikTok and others"
সিফাত নামাজ নিয়ে গালাগালি কেনো করছো আল্লাহ তুমায় ছাড়বেনা,0,"Meme, TikTok and others"
এমন ছেলে আসলে আমার বলার ভাষা খুজে পচ্ছি না,0,"Meme, TikTok and others"
পাগলের বাচ্চা,0,"Meme, TikTok and others"
ছোটো লোক রানু মানদোল,0,"Meme, TikTok and others"
যখন ভাংল তখন কি করছিল এই পয়সা ওয়ালা লোকটা যে নাকি একটা চোর ক্ষয়িষ্ণু সরকারের তাকে একদম বিশ্বাস করবেন না,0,"Meme, TikTok and others"
আপনি এর সম্পর্কে জানলেন কি ভাবে,0,"Meme, TikTok and others"
এই জালিমরে আমার সামনে পেলে ইচ্ছে মত পিটাইতাম,0,"Meme, TikTok and others"
হাসিনারে শুুধ,0,"Meme, TikTok and others"
এখন তোর সাথে মিলন করবে শাকিব তোর নাকি খুব বড়,0,"Meme, TikTok and others"
আমার মনে হয় আপনার ও কম নয় কি ঠিক বললাম তো,0,"Meme, TikTok and others"
উচ্চারণ ঠিক করেন,0,"Meme, TikTok and others"
আপনে কি বেষা সত্যি কি ঠিক কইচে,0,"Meme, TikTok and others"
কাশ্মিরের সাধিনতা চাই,0,"Meme, TikTok and others"
আমার চয়েস হয়নিআমারে দিলেও যামু নাআমার কাছে ভাল্লাগে নাই,0,"Meme, TikTok and others"
অরে বাবা করছে কি কি অবছতা এইডার,0,"Meme, TikTok and others"
রাস্তার কুত্তার জায়গা রাস্তায় মানুষ এর বিছানায় নয়,0,"Meme, TikTok and others"
উনার প্রতিটা থাপ্পড় আমার কলিজা টা ভেঙে টুকরো টুকরো করে ফেলেছে আমি আমার চোখের জল ধরে রাখতে পারলাম না এই ভিডিওটা দেখার পর থেকে আমি অনেক কেদেসি ওকে ফাঁসি দেয়া হোক,0,"Meme, TikTok and others"
ওকে যদি হাতের কাছে পাই তাম বোঝায় দিতাম,0,"Meme, TikTok and others"
স্ত্রীকে ভালবেসে দশমীর মিষ্টি খাওয়ানোর অপরাধে বৃদ্ধবাবাকে নির্যাতন করলো পাশন্ড ছেলে এই যে ভদ্র মানুষ রুপী জানোয়ারের ছবি দেখছেন নামঃ প্রদীপ বিশ্বাস বাড়ি ভারতের পশ্চিমবঙ্গের অশোকনগর বিল্ডিং মোড় কাঠগোলার পাশে উত্তর পরগনা নিচে তার আইডির লিংক দেওয়া হল নিজের বৃদ্ধ বাবাকে কেমন করে মারছে আর তার স্ত্রী দুয়ারে দাড়িয়ে তামাসা দেখছে দেখুন এদের গায়ে কি আদও মানুষের রক্ত আছে তুইও একদিন অক্ষম ছিলি তখন তোকে মানুষ করেছে এত বড় হয়েছিস চলে ফিরে বেড়াচ্ছিস তাদের দয়াতেই তোর সমস্ত ভারদায়িত্ব নিয়েছে বৃদ্ধ হলে মানুষ সক্ষমতা হারায় তাদের যত্ন করা আমাদের কর্তব্য তাদেরও ভরনপোষন করতে হয় আর সেই বৃদ্ধ মানুষটাকে এভাবে মার বাঃ হয়তো এসব দিন দেখার জন্যেই বাবামায়েরা বুকের রক্ত জল করে এরকম অকৃতজ্ঞ অমানুষদের বড় করে তোলেন দয়া করে পোস্টটি শেয়ার হোক হোক ভাইরাল যেন আইনের চোখে ব্যাপারটি পরে আর এই আবালের বিরুদ্ধে উপযুক্ত ব্যবস্থা নেওয়া হয় ক্রেডিট প্রণয় বিশ্বাস সংগ্রহঃ,0,"Meme, TikTok and others"
ওরে পুলিশের হাতে তুলে দেয়ার আগে সবাই মিলে ওকে পিটিয়ে আধমরা করলো না কেন,0,"Meme, TikTok and others"
তোমার সাথে কথা বলতে চাই,0,"Meme, TikTok and others"
মুদি জঙ্গী বাহিনীর হাত থেকে কাশ্মীর রক্ষা পারে ইনশাআল্লাহ,0,"Meme, TikTok and others"
মানুষ কি ভাবে এতটা খারাপ হয়,0,"Meme, TikTok and others"
টিক আছে ভাই,0,"Meme, TikTok and others"
নষ্ট মেয়ে,0,"Meme, TikTok and others"
মানুষ যে এতো খারাপ হতে পারে রানূ দির মেয়ে কে দেখে বোঝা গেলো অতি লোভ ওর,0,"Meme, TikTok and others"
ওরা দুজনে বড় ও বউ পাবে কিন্তু ছেলে টার দিকে তাকিয়ে ওদের এক হয়ে জায়া উচিত আসা করি বুঝতে বারছেন,0,"Meme, TikTok and others"
ওকে ফসি দেওয়া হোক,0,"Meme, TikTok and others"
কথা ঠিকি বলছোসটলিউডে তোর মতো প্রতিবন্ধী কেউ নাই,0,"Meme, TikTok and others"
আমি আসবো নামবার দিলাম কথা বলো আমার সাথে,0,"Meme, TikTok and others"
ভাইওকেপিটানকেমালখোলাগারসনথান,0,"Meme, TikTok and others"
ওর মতো জানোয়ার বেঁচে থাকার চেয়ে মরে যাওয়া ভালো,0,"Meme, TikTok and others"
আল্লাহর কসম কোরআনের শিক্ষা না থাকার কারনেই এই অবস্থা,0,"Meme, TikTok and others"
ধন্যবাদ জানাই যিনি ভিডিও করে মহা ধর্মের কাজ করেছেন এভাবেই সম্ভব সমাজের কল্যাণ ছেলেটি তো স্তৈন,0,"Meme, TikTok and others"
ফাঁসি তার আগে গবর খেতে দিতে হবে আমার অনুরদ,0,"Meme, TikTok and others"
সত্যি দুঃখ প্রকাশ,0,"Meme, TikTok and others"
আপু আপনার নিজের দুধই তো ঝুলে গেছে ব্রা দিয়ে টাইট করে আটকে রাখছেন আমরা জামার উপর দিয়ে শেইপ দেখলেই বুঝি কার দুধ কেমন,0,"Meme, TikTok and others"
দেখেতো এমন মনে হইতেছে বাবা ছেলেকে পিটাচ্ছে এই শাস্তি কখনো মাফ করার মতো নয় পৃথিবীতে তো বিচার হবেই আর আখিরাতেও তার বিচার হবে,0,"Meme, TikTok and others"
পুলিসের বিচার চাই,0,"Meme, TikTok and others"
ডুগডুগি মতিয়ার খবর কি,0,"Meme, TikTok and others"
কিছু বলার ভাষা নাই,0,"Meme, TikTok and others"
খুব বাংলায় এর ভাষন দিলেনতবে সাবধান ইসলাম নিয়ে খারাপ কিছু বল্লে সমস্যা আছেএখন ও সময় আছে তওবা কর,0,"Meme, TikTok and others"
কাশ্মীর স্বাধীন হবেই ইংশ আল্লাহ,0,"Meme, TikTok and others"
কুয়েত থেকে দেখছি আমরা মসজিদ চাই মারা মারি চাই না,0,"Meme, TikTok and others"
অবশ্যই পাকিস্তান আপু,0,"Meme, TikTok and others"
বুখারি ই সব নয় বুখারি কেমন মুসলিম থেকে বাদ দেওয়া হোক,0,"Meme, TikTok and others"
আল্লার কছম অই ছেলেরে যদি আমি পাই জবাই করে মৃত্যু দিতাম,0,"Meme, TikTok and others"
কাপড়টা তোলে পাছায় দুইটা দিবদুষ্ট মেয়ে ভারত উককাইয়া রাখছেআইলেই লাগাতে পারবি,0,"Meme, TikTok and others"
আমার নাম জসীম আমি একজন ভালো ভনদু চাই টাকার বিনিময় করা জায় বন দুহওয়া জায় না এটা আমার নাবার,0,"Meme, TikTok and others"
আমার সামনে পেলে তাকে জুতা দিয়ে ভালো করে মারতাম যতখন আমার হাত না বেথা হয়,0,"Meme, TikTok and others"
ওর মায় ওরে কি খাইয়া জন্ম দিসেকইতে পারেন🤣🤣🤣,0,"Meme, TikTok and others"
জাকির নায়কের বিরুদ্ধে কট্টর হিন্দুত্ববাদী ভারত সরকারের এটি একটি চক্রান্ত মাত্র হিন্দু ধর্মাবলম্বী বেদম হারে ইসলাম ধর্ম গ্রহণ করছে বলে জাকির নায়ক কে অপবাদ দিয়ে ভারত সরকার চায় হিন্দু কনভার্সন বন্ধ করতে আমার হাতে ক্ষমতা থাকলে আমি এক্ষুনি মিথ্যাচারী ভারত সরকারের বিরুদ্ধে যুদ্ধ ঘোষণা করতাম,0,"Meme, TikTok and others"
নরেন্দ্র মৌদির ফাঁসি চাই উপযুক্ত শাস্তি চাঁই এইসব অনৈতিক নিষ্ঠুর আচরণের তীব্র নিন্দা ধিক্কার জানাই অমানুষিক অমানুবিক জুলুম নির্যাতন বন্ধ হউক চিরতরে,0,"Meme, TikTok and others"
এরকম বাঘ বার বার জন্মায় না ৷ নেড়ি কুত্তাগুলোই ঘেউ ঘেউ করে ৷ বাঘে গর্জন করে ৷,0,"Meme, TikTok and others"
এর বিরুদ্ধে প্রতিরোধ গড়ে তোলা উচিত,0,"Meme, TikTok and others"
কোন মনুষ কেমন তা তার চরিত্র দেখে জানা জায় এটা কোন জেলা ভিত্তিক নয় যে কোন জেলার মেয়েরা ভালো বা খারাপ হতে পারে এমন কোন কথা নেই যে অমুক জেলার মেয়েরা সবাই ভালো তমুক জেলার মেয়েরা সবাই খারাপ,0,"Meme, TikTok and others"
ভালোই করছে,0,"Meme, TikTok and others"
ভাই আমার জানা মতে ভারত পাকিস্তান ও বাংলাদেশ মানুষ ও ভাষা আচার অনুষ্ঠান রং ঢং এক রকম তাই হিংসা বিন্ধেস বাঁধ দিয়ে এক হলে চিন আমেরিকা পতলা পায়খানা করে দিবে,0,"Meme, TikTok and others"
আপনার বাংলা উচচারণ শুনে আমার শরীর ঝিম ঝিম করতেছে,0,"Meme, TikTok and others"
বাল ফালাবে,0,"Meme, TikTok and others"
তোমার নামবার দাওআমি বিদেশে থাকি,0,"Meme, TikTok and others"
ইনশাআল্লাহ আমারা সবাই জয় বাবুর পাসে আছি জয় বাবু তুমি এগিয়ে যাও অনেক অনেক দোয়া রইল সবার জন্য আশা করি আপনারাও দোয়া করবেন তাদের ফেমেলীটার জন্য ধন্যবাদ সবাইকে,0,"Meme, TikTok and others"
হাই সুন্দরী মাল,0,"Meme, TikTok and others"
জাকিরনায়েক নিরদোষ,0,"Meme, TikTok and others"
বাবা সাকিবকে না পেয়েও আবরাহাম জনমো দীন করলোকেন,0,"Meme, TikTok and others"
সবি স্টার জলসার কল্যাণ ☺,0,"Meme, TikTok and others"
পুরুষ উপস্থাপক নেওয়া ঠিক হয়নি বিকজ আমরা মুসলিম,0,"Meme, TikTok and others"
মাবদ,0,"Meme, TikTok and others"
ওনার টা জে যুলে গেছে সে খেয়াল আছে,0,"Meme, TikTok and others"
পুলিশরা সব চোর,0,"Meme, TikTok and others"
শাকিবের অনেক ভক্ত ছিলাম এখন নাম শুনতেই ঘৃনা হয় এত সুন্ধর অপুর জন্যেই শাকিবকে অনেক সুন্ধর লাগতো কিন্তু বুবলি চিকার থোতার কাছে গেলে সুপারস্টার শাকিবের চেহারার উজ্জলতাই নষ্ট হয়ে যায় এবং কোনো ভাবেই তাকে সুপারস্টার মনে ই হয়না শাকিবকে একমাত্র সুন্ধর লাগে অপুর পাশে থাকলেই,0,"Meme, TikTok and others"
ওর শাস্তি হওয়া উচিত আমরা ওর শাস্তি চাই আপনারা সবাই সোশ্যাল মিডিয়াতে ওর জন্য শাস্তি দাবি করুন যেন ওকে আইনের আওতায় এনে শাস্তি দেয় জাযাকাল্লাহ খায়ের,0,"Meme, TikTok and others"
অপুকে সাকিবকে দেখতে চাই,0,"Meme, TikTok and others"
দুনিয়াতে তোমার সব চাইতে আপন জন হলো আল্লাহ তারপর মা বাবা মা বাবাকে কষ্ট দিলে আল্লাহর আরস কেপে উঠে মা বাবা হলো বেহেস্তে যাওয়ার রাস্তা,0,"Meme, TikTok and others"
নিজের জান বাচানোর ক্ষেত্রে কিছু কথা অনলাইনন এ আমি বলি না কিন্তু আমার কথা আপনি বলে দিয়েছেন আপনি হচ্ছে লিজেন্ড,0,"Meme, TikTok and others"
ভিডিওটা দেখতে চাই,0,"Meme, TikTok and others"
মেহেজাবীন চৌধুরি,0,"Meme, TikTok and others"
কলকাতা এগুলো অহরহ দেখা আকাডার বাচ্চারা ইন্ডিয়াতে কোন প্রশাসন নেই এদের বিচার করে না কেন,0,"Meme, TikTok and others"
ওরা এমন কেন,0,"Meme, TikTok and others"
ছাগল উপস্থাপিকা,0,"Meme, TikTok and others"
আমরা চাই যেনো ওরা দুজন এক হক দোজন,0,"Meme, TikTok and others"
মমতা ব্যানার্জি যদি ভারতের প্রধান মন্ত্রী হন পুরো ভারত বদলে যাবে ভারতের প্রধান মন্ত্রী হওয়া উচিত মমতা ব্যানার্জি,0,"Meme, TikTok and others"
আপনাদের ওপর শরম লাগে এখানে মারছে আর আপনি ভিডিও বানাচ্ছেন,0,"Meme, TikTok and others"
কাশ্মীরে পখে,0,"Meme, TikTok and others"
আখি আলমগীর আদমজি কলেজে পড়ত আর আমি তখন আদমজি স্কুলে পড়তাম উনার ভাই তাসবির আমার সাথেই পড়তএরাতো পড়লেখার কচুও পারতোনা টাকার জোরে ভাল প্রতিষ্ঠানে পড়ার সুযোগ পাইছে,0,"Meme, TikTok and others"
দিদি ঠক ও মিথ্যাবাদিও বটে,0,"Meme, TikTok and others"
পক্ষে নাই,0,"Meme, TikTok and others"
আমি কাশ্মীর পোখে আছি বহাল থাকুক,0,"Meme, TikTok and others"
বেশি বেশি নামাজ পড়লে ভালো হবে,0,"Meme, TikTok and others"
কোন দেশে সংখ্যালঘু নির্যাতন হওয়া এটা সম্পূর্ণ উদ্বেগের বিষয় এই বিষয়ে আমি পুরোপুরি উদ্বিগ্ন,0,"Meme, TikTok and others"
পশু একটা,0,"Meme, TikTok and others"
আপু পাপন কে একপোটা দুদ দাও,0,"Meme, TikTok and others"
বাদ দে,0,"Meme, TikTok and others"
ও নারি না ও নারি নামের একটি হিজরা কারন হিজরা দের লজজা নাই ওকে আপনারা চেক করেন ওর সব ফাস হয়ে জাবে ওর সব পিলাশ টিক ছার জারি করা,0,"Meme, TikTok and others"
মানুষ মানেই তো বাইমান এর জন্য আমি পশু প্রেমী এক মত হলে করুন,0,"Meme, TikTok and others"
তোদের দেখলে মনে হয় মৃত্যু নামক জিনিস ভোদয় দুনিয়াতে নাই এসব করে আল্লাহর কাছে কি জবাব দিবি,0,"Meme, TikTok and others"
এ পেসটা লাগিয়েছে মাগিটাজানোয়ার টা জন্মদাতা বাবার গায়ে হাততুলাতোর হাত পোচে যাবে,0,"Meme, TikTok and others"
একটা প্রশ্নের জবাব দিতে পারবেনহটাৎ কেন এতো মাথা কাটা লাশ উদ্ধার হচ্ছে,0,"Meme, TikTok and others"
আমি দেখবো এইগুলা,0,"Meme, TikTok and others"
বাই বাবা টার একটা বেবতা নেন নাহলে ছেলের বউ আর মারবে,0,"Meme, TikTok and others"
কুওর ব্যাঙ সাগরে পরছেত তায় এই দশা,0,"Meme, TikTok and others"
ওকে ফাসির কাস্টে ঝুলানো উচিত,0,"Meme, TikTok and others"
আর বাংলাদেশের সরকার কি করবেন,0,"Meme, TikTok and others"
যার বাবা নেই সে বুঝে আমি যদি তাকে পাইতাম তাকে লাথি মেরে মেরে ফেলতাম,0,"Meme, TikTok and others"
আলহামদুলিল্লাজাকিরনায়কভালোমানুষ,0,"Meme, TikTok and others"
অকে মেরে ফেলতে হবে,0,"Meme, TikTok and others"
পাৱেবে,0,"Meme, TikTok and others"
বিষয় টি অনেক দুঃক্ষ জনক সত্যি এমন করে বাবাকে থাপ্পড় মারা অনেক লজ্জাজনক পাশে ছেলেটি বউ দাঁড়িয়ে একটুও বাধাদেয়নি সত্যি বাবা তুঁমি মহান তার পরেও বলেছ আমি কাওকে বলিনি আমার ছেলে মেরেছে আমার চোখে পানি এসেগেছে মন্টা অনেক খারাপ লাগলো ছেলেটির বউ কেও বিচারের আওতায় আনা উচিৎ,0,"Meme, TikTok and others"
জানোয়ার মর,0,"Meme, TikTok and others"
আমি মনে করি আমাদের বাংলাদেশে ও যারা এমন করে মা বাবাকে অত্ত্যাচার করে তাদেরকে সাথে সাথে পুলিশকে দিয়ে দরিয়ে দিতে হবে,0,"Meme, TikTok and others"
এটা ইন্ডিয়া ইন্ডিয়ায় এরকম জঘন্য ঘটনা হওয়াই স্বাভাবিক কারন ওদের ধরম টা দেখতে হবে না আমাদের দেশে এটা হলে ওই লোক কে জনগন পিটিয়েই মেরে ফেলত পুলিশে নেওয়ার কোন দরকার হত না বাংলাদেশ থেকে এর তিব্র নিন্দা জানাই,0,"Meme, TikTok and others"
ওরে মারা উচিত,0,"Meme, TikTok and others"
যে প্রেম বিছানা পর্যন্ত যায় সেটা কখনোই পরিনতি পায় না,0,"Meme, TikTok and others"
আমি এই আইনের সম্পূর্ণভাবে বিপক্ষে,0,"Meme, TikTok and others"
ঔ হারামির ফাঁশি চাই,0,"Meme, TikTok and others"
সাকিব অপু কে খুব ভালো লাগে,0,"Meme, TikTok and others"
কাশ্মীর পাকিস্তান,0,"Meme, TikTok and others"
একে আমার কাছে দেন ওকে আমি কুরবানি দিমু জেল খাটমু,0,"Meme, TikTok and others"
ওর গলায় পাশ দিয়ে তারপর মারতে হবে,0,"Meme, TikTok and others"
সবাই#,0,"Meme, TikTok and others"
কই এক দিনও দেকলাম না,0,"Meme, TikTok and others"
সারা পৃথিবীর মুসলমানেরা যদি আজ একতাবদ্ধ হয়ে যায় তাহলে বাবরি মসজিদ ভাঙ্গা তো দূরের কথা তোমরা পালাবার পথ খুঁজে পাবে না ইনশাআল্লাহ সময়ের অপেক্ষা করো আল্লাহর আযাবের,0,"Meme, TikTok and others"
শোন যেটা হিন্দুদের সেটা নিয়ে ছারবো আর যেটা হিন্দুদের নয় সেই দিকে তাকিয়ে দেখি না বাবরিমসজিদ তোদের নয় ওটা আগে আমাদের রামের মন্দির ছিল তাই জন্য বলছি অন্য জনের কথায় কান দিসনাতোরা যদি ভগবান কে বিশ্বাস করিস তাহলে সত্যি করে বল ওটা আগে মন্দির ছিল নাকি মসজিদ,0,"Meme, TikTok and others"
আপু একটা ওরনা ব্যাবহার করলে ভাল হয়,0,"Meme, TikTok and others"
আল্লাহ তুমি এই জানোয়ারের হাত টা অবশ করে দাও যেন কোন কাজ না করতে পারে,0,"Meme, TikTok and others"
ভাষা শুনে ও মন্তব্য করেছেন যারা তাদের ধর্মীয় সংখ্যা দেখে বোঝা যাচ্ছে আপনি বাংলাদেশি তাহলে মিথ্যে কেন বলছেন কলকাতা থেকে বলছেন,0,"Meme, TikTok and others"
ওকে জেলে দেন,0,"Meme, TikTok and others"
আমি একজন বাবা আর এই দৃশ্য দেখে আমার চোখে পানি এসে গেলো আমি তার পাসি চাইএকমতথাকলে লাইক দিন,0,"Meme, TikTok and others"
ওরে জুতা মারার দরকার,0,"Meme, TikTok and others"
বে সরম মেয়ে,0,"Meme, TikTok and others"
তোর ভালো করে অর্গাজম হয়না তাই পড়িস যদি একটু মনে শান্তি পাওয়া যায়,0,"Meme, TikTok and others"
শাকিব অপু বেষ্ট জুটি আবার চাই এই জুটি,0,"Meme, TikTok and others"
লোবি মেয়ে মা যখন ভিঙ্খে করত তখন মায়ের কোন খুজ খবর নিলনা এখন যে দেবতা রুপি মানুষ টির জন্য আজ রানো মন্ডল এত উপরে উঠল আজ কিনা তার বিরুদ্ধে মন্তব্য করছে লাজ হিনা মেয়ে লজ্জা বলতে যদি কিছু থাখে তা হলে এখন আর নিজের মা বলে পরিচয় দিতনা রানু মন্ডলের উচিত এখন এমন মেয়েকে তেজ্য মেয়ে ঘুষনা করা যদি রানু মন্ডল ও মেয়ের মত না হয় তা হলে তার আস্রয় দাদা অথিন্দ্রর সম্মানবাছাছবে রানু মন্ডল আর রানু মনাডল ও যদি মেয়ের মতো বাজে হয় তা হলে মেয়েকে প্রধান্য দেবে,0,"Meme, TikTok and others"
ধন্যবাদ,0,"Meme, TikTok and others"
জাকিনায়ক ইছলামেৰ গৈৰভ,0,"Meme, TikTok and others"
দয়াকরে আপনাদের এই ভুল মন্তব্যগুলো বন্ধ করুন কলকাতায় সাকিব খানের চাহিদা ℅ নেই এর একটাই প্রমাণ হল উনার একটিও সিনেমাও এপার বাংলায় হাউসফুল হয়নি এবং সত্যি ঘটনা উনি বড় অভিনেতা হতেই পারেন কিন্তু কলকাতায় দর্শক উনার থেকে জয়া ইয়াসানকে বেশি পছন্দ করে দেব জিৎ বলে নয় এপার বাংলায় সিনেমার দর্শক ভালো সিনেমা দেখতে পছন্দ করে নায়ক নায়িকা নয় তাই রসগোল্লা#র মতন সিনেমাও সপ্তাহেও হাউসফুল হয় ধন্যবাদ,0,"Meme, TikTok and others"
না না না,0,"Meme, TikTok and others"
ওরে আজকে মাইরালা অসহায় ব্যক্তিকে এভাবে মারে,0,"Meme, TikTok and others"
কাশ্নীর,0,"Meme, TikTok and others"
এই বাবার জুতা দিয়েই বাবার দিয়েই পিটানো উচিত ছিল,0,"Meme, TikTok and others"
আমি খুব খুশি ও খালি কাজে থাকে তাও বউ পুলা বাতদিযা খুব খুশি,0,"Meme, TikTok and others"
কাশমির পক্ষে,0,"Meme, TikTok and others"
এ মনে হয় ভারতের ভালোমতো বাংলা বলতে শিখে নি,0,"Meme, TikTok and others"
সত্য বলছেন তো,0,"Meme, TikTok and others"
তুই রবটের মত কথা কস্ ক্যা,0,"Meme, TikTok and others"
হাচিনার আমলে আর কত কি দেখবো,0,"Meme, TikTok and others"
কাশ্মীর স্বাধীন হোক আমরা চাই তবে হ্যাঁ মুদির দখলের না যেন পড়ে মুদি বহুৎ খারাপ মানুষ,0,"Meme, TikTok and others"
তাহলে ছেলেরাও কি আন্ডারপ্যান্ট পরে ছবি দিলে তাহলে কি তারাও নায়ক হয়ে যাবে,0,"Meme, TikTok and others"
আপু আপনাকে কথা গুলো বলার জন্য,0,"Meme, TikTok and others"
ঘটনাটা আসলেই দুঃখজনক আমি বা আমরা চাইনা কেউ এমনটা আমাদের দেশে হোক কলকাতার এমন নিউজ আমাদের দেশীয় টিভি চ্যানেলে প্রচার করার মানে কি জানতে চাইছি ভারত প্রীতি ছাড়ুন দয়া করে আমাদের দেশের প্রতি নজর দিন আমাদের দেশে হাজারো বৃদ্ধ্যাশ্রম আছে আগে দেশ বাচান তারপর ভারতপ্রীতি দেখান,0,"Meme, TikTok and others"
আপা চৈতালি নামের অর্থ কি,0,"Meme, TikTok and others"
থাড় কেলাশ রানু,0,"Meme, TikTok and others"
ওর পেছনে গরম রাজহাঁসের ডিম ঢুকাবেন,0,"Meme, TikTok and others"
সৌদি বাংলাদেশ পুটক মারলো,0,"Meme, TikTok and others"
এও কি সম্ভব কোনো পিতা মাতা কি কখনও ভাপতে পারে নিজের ঔরসজাত সন্তান যাকে নিজে হাজার কষ্টে থেকে ও নিজের সন্তানকে একটু কষ্ট পেতে দেয়নি সেই সন্তানের হাতে এভাবে চর থাপ্পর খেতে হবে ছি আর তার বউটা একটু প্রতিবাদ ও করেনি কেমন মায়ের সন্তান এইগুলি ছি,0,"Meme, TikTok and others"
বাবা খাছ নাকি,0,"Meme, TikTok and others"
প্রত্যেক নায়িকারাই পুরুষদেরকে যৌন উওেজনা দেয়,0,"Meme, TikTok and others"
রানুকে আবার ষ্টেশনে বসিয়ে দিন,0,"Meme, TikTok and others"
একটা জিনিস স্পষ্ট এই বিলের ফলে প্রতিবেশী দেশর সংখ্যালঘুদের চরম বিপদের পরতে হতে পারে,0,"Meme, TikTok and others"
যদি এই সংবাদ স্যতিই হয়তাহলে মহা খুশি হবএর চাইতে আর ভাল খবর নেই,0,"Meme, TikTok and others"
আগে চিল এখন পাগল তবে খারাপ পাগলপিচনে্ বাশ দেওয়া উচাচ,0,"Meme, TikTok and others"
অহংকার পতনের মূল কারণ যদি রানুদি এই সমস্ত কথাগুলি বলে থাকে তাহলে আমি সিওর ওকে আগের অবস্থায় ফিরে আসতেই হবে যে জনগণ ভাইরাল করে ওকে ঐ জায়গায় পৌঁছেছে সেই জনগণই ওর সমালোচনা করে ওকে আবার সেই স্টেশনের জায়গায় ফিরিয়ে দেবে আর ভিখারি এবং মাথায় উকুন নিয়েই থাকতে হবে,0,"Meme, TikTok and others"
আপনারা একি ছবি দেখাচ্ছেন কারণ কী,0,"Meme, TikTok and others"
জবা খুব ভালো লাগছে,0,"Meme, TikTok and others"
ডাঃ জাকির নায়েক খুব সুন্দর একটা মানুষ,0,"Meme, TikTok and others"
আজিবন আনলিমিটেট ফোনইমু সরাসরি রিয়েল সেক্স সার্ভিস আমি নয়ন ভাই আমার কাছে অসংস্য সেক্সী ভাবি আছে আমি নয়ন সওদাগর ভাই,0,"Meme, TikTok and others"
সাকিব এর কথাটি যথার্থ সত্যি কথাই বলেছেন,0,"Meme, TikTok and others"
মোদীর ফাসি চাই,0,"Meme, TikTok and others"
হায়রে অভাগা সন্তান,0,"Meme, TikTok and others"
রিয়েল বলসে পপি,0,"Meme, TikTok and others"
তোমরা মারামারি করো কিন্তু আমাদের অধিকার কেরে নাও কেনো আমরা তো খেটে খাওয়া মানুষ আমার ছেলের চাকরি কেনো কোটার কারনে হবেনা আমি এক দেশে বাস করে কেনো কর বেশি দিব অন্যদের থেকে আমরা তো কোন দলে বলে নেই,0,"Meme, TikTok and others"
নেইমার,0,"Meme, TikTok and others"
এর কাজ দেখলে পায়ের রক্ত মাতায় উঠে যায়,0,"Meme, TikTok and others"
রানুকে ছুঁয়ে ফেলেডেয়,0,"Meme, TikTok and others"
পা ও কা,0,"Meme, TikTok and others"
অর ফাসি চাই,0,"Meme, TikTok and others"
ভারতের পক্ষে,0,"Meme, TikTok and others"
ক্ষমা করা হল,0,"Meme, TikTok and others"
মার মালুনকে আর ছাড়না,0,"Meme, TikTok and others"
ছোট বেলা থেকে বাবা মা কত কিছু করে সন্তানের জন্নো আর বড় হোয়ে তারা এই করে কি আর বলিকোসে মার দেয়া দরকার ছেলে টাকে,0,"Meme, TikTok and others"
যদি এই খবর টা সত্যি হয়ে থাকে তাহলে অনেক অনেক খুশি হব কারন টাকা পয়সা তো আর ছেলে বউ বাচ্চার চেয়ে বড় নয় আর আমরা চাই না আব্রাহাম তাহার বাবা কে ছেড়ে এতিমের মতো ঈদ করুক সাকিব আব্রাহাম কে এখন একটু সময় দেও প্লিজ,0,"Meme, TikTok and others"
মোদির নাকের উপর দাড়িয়ে পুনরায় বাবরি মসজিদ পূনরায় নির্মাণ করব ইংশাআল্লহ আল্লাহ গো খোরের হাত থেকে মুসলমানদের রক্ষা কর,0,"Meme, TikTok and others"
কাশমিৱ,0,"Meme, TikTok and others"
দুধ নাকি ডোন,0,"Meme, TikTok and others"
ভাগ ঠিক হয় নি,0,"Meme, TikTok and others"
তুই যেন আর জেল থেকে আর না বাইরে বের হস,0,"Meme, TikTok and others"
হোটেল মনি মুকতা আবাসিক আমরা হোম সার্ভিস দিয়ে থাকি আমি আরিফ ভাই,0,"Meme, TikTok and others"
অযোধ্যায় বাবরি মসজিদ যদি না থাকে ভারত ধ্বংস হয়ে যাবে,0,"Meme, TikTok and others"
ওর মতো নারী বাংলাদেশ থেকে বের করে দেওয়া উচিত শাকিব যা বলেচে তা কম বলেছে ওকে বাজারে নামিয়ে দেওয়া উচিত,0,"Meme, TikTok and others"
আসালামু ওয়া লাইকুম আমি গরবিতো আমি একজন মুসলিমের সন্তান তাই মুসলিমের সান্তি ছাই ভারত মিদী জংগি গুড্না ভাহিনি কে ওচিত সিক্ষা দিন ইমরানকান কে ধন্দৌভাদ,0,"Meme, TikTok and others"
সানাই কেনো এত টাকা খরচ করতে গেল এনার থেকে টিপস নিয়ে বড় করতে পারত,0,"Meme, TikTok and others"
আমি পপি কে বিয়ে করতে চাই কানাডা থেকে বলছিকেউ পারলে জানাবেনসত্যি বলতাছি,0,"Meme, TikTok and others"
সবাই বেশি বেশি করে শিয়ার করুন ওনার গালে থাপর মারা জে সবার বাবার গালে থাপর মারা এক সমান,0,"Meme, TikTok and others"
অামরা জনগণ চাই অপু বিশ্বাস ও শাকিব খান এক হোক পিলিজ পিলিজ পিলিজ পিলিজ অাপনারা চেষ্টা করেন,0,"Meme, TikTok and others"
কাস্মির স্বাধীন চাই,0,"Meme, TikTok and others"
ঠিকেই বলছে সবাই ভগৱানৰ চাকৰ,0,"Meme, TikTok and others"
ঠিক আচে,0,"Meme, TikTok and others"
ওর চাকরি থেকে বরখাস তো করা উচিত,0,"Meme, TikTok and others"
প্রিয়া সাহার কথা মিথ্যা নয় হিন্দু ইতিহাস ভিডিও,0,"Meme, TikTok and others"
কি হয়েছে,0,"Meme, TikTok and others"
বুড়া বাবা হাঠতেও পারছে না তাকে মারলো,0,"Meme, TikTok and others"
আল্লাহর বিনা হুকুমে কোন একটা গাছের পাতা নড়েনা অতএব আমরা আল্লাহর উপর নয়,0,"Meme, TikTok and others"
পুলিশ ভাইদের বলছিএই জানোয়ারটা কে পিটাইলে আপনাদের পুলিশের চাকরি করাটা সার্থক হবে ভাই,0,"Meme, TikTok and others"
মিতা নিউজ দিয়ে কি লাভ সব থেকে ভালো বিকা করে খাওয়া,0,"Meme, TikTok and others"
বুবলি তুমিএগিয়ে যাও আমরা তোমার সাথে আছি,0,"Meme, TikTok and others"
মসজিদ আছে আর তাকবে,0,"Meme, TikTok and others"
আমি কাস্মির,0,"Meme, TikTok and others"
দোস্তোর ভিডিও গুলা দেখি অনেক মজা পাই,0,"Meme, TikTok and others"
কথা কইতে পারেনা,0,"Meme, TikTok and others"
যতোই হক বাবা এর গায়ে হাত উঠানো বড় অপরাদওজে সাজা দেওয়া হোক,0,"Meme, TikTok and others"
হ আমরা ও চাই,0,"Meme, TikTok and others"
এলাকাবাসী কোথায় এলাকাবাসী চোখে পড়ে না নিম্ন তারা বিচার করতে পারে,0,"Meme, TikTok and others"
আমাদের সমাজ ব্যবস্থায় এরকম অনুষ্ঠান মোটেই মানানসই নয় পশ্চিমা সভ্যতার সাথে বাংলাদেশী সভ্যতার সংকরায়ন করলে যে সভ্যতার জন্ম হয় সেটা হয়তো খুব আপত্তিকর অথবা হাস্যকর হয়,0,"Meme, TikTok and others"
সাকিব ভাইয়ের সাথে আমি একমত,0,"Meme, TikTok and others"
পুলিশ অফিসার কে অনেক ধন্যবাদ ফাজিল ছেলেকে ধরে নেয়ার জন্য,0,"Meme, TikTok and others"
ভারত কাহকে ভয় করেনা,0,"Meme, TikTok and others"
সঠিক বিচার হয়চ্ছে,0,"Meme, TikTok and others"
ম্বধীন কাশ্মীর চাই,0,"Meme, TikTok and others"
পুরুষ যৌন কর্মীর ফোন নাম্বার,0,"Meme, TikTok and others"
তুই বাংলাদেশে চলেযা মটা টাকা পাবি,0,"Meme, TikTok and others"
মানুষ এত খারাপ হয় ছি ছি দুঃখ হয়,0,"Meme, TikTok and others"
অামরা মুসলিম তাই আমাদের মুসলিম কান্টি করা দরকার,0,"Meme, TikTok and others"
বাবাকে মারার জন্য ছেলেকে মুত্যুদন্ড দেওয়া উচিত তা দেখে যেন আর কোনও ছেলে বাবার গায়ে হাত তুলতে সাহস না পায়,0,"Meme, TikTok and others"
আমি,0,"Meme, TikTok and others"
ফিরে গেলে ভালো,0,"Meme, TikTok and others"
শিক্ষা না থাকলে যা হয় আর কি,0,"Meme, TikTok and others"
থথথথথথ,0,"Meme, TikTok and others"
ভারতের ঘটনা কথায় মনে হচ্ছে,0,"Meme, TikTok and others"
মুরুকো,0,"Meme, TikTok and others"
জানোয়ার একটা,0,"Meme, TikTok and others"
শয়তানের বাচ্চা কে পুলিশে দিতে হবে,0,"Meme, TikTok and others"
কাশ্মীর নিয়ে ভারতের মাথা ব্যাথা কেন আমরা চাই কাশ্মির স্বাধীন রাস্ট হবে,0,"Meme, TikTok and others"
তোরা দূশি মিথ্যা পচার করচ একটা লাইকের জন্য,0,"Meme, TikTok and others"
আল্লাহ মাফ করো কান্না পাচ্ছে খুব এ কেমন ছেলে আল্লাহ তুমি হেফাজত করো,0,"Meme, TikTok and others"
মানুষের হাতে দুই চার পইসা চলে আসলেই এই রকমেই হই,0,"Meme, TikTok and others"
পাকিস্থান বিজয় হওক,0,"Meme, TikTok and others"
আমারা চাই আবারো সাকিব এবং অপুর জুটি হোক,0,"Meme, TikTok and others"
যোগ্যতার চেয়ে বেশি পাওয়াতে এই অবস্থা,0,"Meme, TikTok and others"
সম্রাটের চেয়েও ইমনকে নিয়ে অনেক ভালো হইছে,0,"Meme, TikTok and others"
তুই খবর নকল করছ কে,0,"Meme, TikTok and others"
ফাঁসিতে ঝুলিয়ে ওর পাপের প্রায়শ্চিত্ত করা হোক,0,"Meme, TikTok and others"
কাস্মীর স্বাধীন হৌক কাস্মীরে কাফের মলাউনের বাচ্ছারা যে হত্যা মুসলিম নারীদেরকে ধর্ষন চালিয়েছে তা নযিরবীহিন হে আল্লাহ তুমি কাফেরদের উপর গজব নাযিল কর আমিন,0,"Meme, TikTok and others"
আল্লাহ আপনি আমাদের কে হেদায়েত করুন,0,"Meme, TikTok and others"
মালাউনের পক্ষে কখনো ও না,0,"Meme, TikTok and others"
ওবে পাশি দাও,0,"Meme, TikTok and others"
প্লিজ ভাই সব অভিমান বুলে দুইজন এক হয়ে যানতাতে আপনার সম্মান নষ্ট হবে নাবরন সম্মান বারবে ছেলে টার বুকটা ও পুরা থাকবে,0,"Meme, TikTok and others"
তাকে ত গুলি করে মারা উচিৎ,0,"Meme, TikTok and others"
মনুষত্ব বলতে কিছুই নেই,0,"Meme, TikTok and others"
মুদিকে খুদি খাওয়া হবে,0,"Meme, TikTok and others"
নিশ্চয়ই আমি আমিন রাজা নরেন্দ্র মোদির বিপক্ষে আমি অবশ্যই পাকিস্তানের পক্ষে হিন্দুস্তানের পক্ষের নয় তবে হিন্দুস্তানের যেসব মুসলমানরা আছে তাদের পক্ষে এক কথা বলা চলে আমি যেতাম মুসলিম আমি অবশ্যই সদাসর্বদাই মুসলিমের পক্ষে থাকবো ইনশাল্লাহ,0,"Meme, TikTok and others"
দোয়া করব,0,"Meme, TikTok and others"
মোদী ব্যাপারে ডেস নয়,0,"Meme, TikTok and others"
এটাকে ডিগ্রি দেওয়া দরকার,0,"Meme, TikTok and others"
এই মেয় মেটে মাসে আগে হয় ছে,0,"Meme, TikTok and others"
এখন পুলিশ মিষ্টি খাওয়াবে ওকে,0,"Meme, TikTok and others"
এই পারমিতাই তো গিয়েছিল প্রধান বিচারপতির বিছানায় তাই সব জানে,0,"Meme, TikTok and others"
কাশ্মীর নিয়ে তোমাদের মাথা ব্যাথা কেন ইতিহাস পড়োনি পাকিস্থান তোাদের কি অবস্থা করেছিল তোমরা তার গান গাইছো ধিক্কার তোাদের,0,"Meme, TikTok and others"
শারুক বা নাইকরা শুধু ছবিতে পারে জিবনে না ভিতু,0,"Meme, TikTok and others"
আমরা সত্যর পক্ষে আছি আর সত্যর জয় হবেই ইনশাআল্লাহ,0,"Meme, TikTok and others"
এক হোক,0,"Meme, TikTok and others"
মিথ্যা কবর,0,"Meme, TikTok and others"
মেছি কে ভাল বাসি সারা জিবন ভাল বেসে জাব♥,0,"Meme, TikTok and others"
শকুন যত উপ‌রেই উঠুকনা কেন নজর থা‌কে নি‌জের দিক,0,"Meme, TikTok and others"
ওরা দুজনে এক হলে লাখো লাখো জনতা খুব খুশি হবে,0,"Meme, TikTok and others"
বুবলি মলে হয় বিবাহিত ছেলেকেই ভালো লাগে লজ্জা করেনা পারলে নিজের জামাইকে অন্যের করে দেখা পরের,0,"Meme, TikTok and others"
বালের গল্প,0,"Meme, TikTok and others"
কৃুমিল্লা কই,0,"Meme, TikTok and others"
খালেদার জতো দালাল সব রাজা কার,0,"Meme, TikTok and others"
ভাই বাডিওটা আমার খুব ভাললাগল,0,"Meme, TikTok and others"
অবশ্যই নির্দোস,0,"Meme, TikTok and others"
ইণ্ডীয়ার জারজ মোদিসন্তানদের এক এক কড়ে খুঁজে মারতে হবে ইণ্ডীয়া টুকরো করতে হবে ইনসা আল্লাহ পাকিস্তান চীন করবে আমিন,0,"Meme, TikTok and others"
আমার কাছে লাগতে চেদুধ একটা বড় একটা ছুট ্্্মনে হয় হাওয়া কমে গেছে একটার,0,"Meme, TikTok and others"
আমরা সবাই তার ফাশি চাই,0,"Meme, TikTok and others"
ভাইয়া অাপনার ফোন নামবারটা দিন অাপনার সাথে কথা বলবো,0,"Meme, TikTok and others"
চোরের আবার বড় গলা,0,"Meme, TikTok and others"
মিথিলার মতো মেয়েদের জরায়ুতে ক্যান্সার হওয়ার সম্ভবনা বেশি,0,"Meme, TikTok and others"
এটাই,0,"Meme, TikTok and others"
তুমাকে আমি কি বলবো খুজে পেলাম না তার পরেও একটা বলতে হবেতর সাতে এই রখম একটা গটনা গটবে বিয়াদব কতাকার,0,"Meme, TikTok and others"
যারা জাকির নায়েককে গ্রেপ্তার করতে চাই আল্লাহ তাদেরকে গ্রেপ্তার করবেন সবকিছুর ক্ষমতা আল্লাহর হাতে,0,"Meme, TikTok and others"
রায় দান কারীর মুখে ও হাতে আল্লাকেনছার অথবা পেরালাইছ রোগ দিবেন নিশ্চয় মসজিদ আল্লার ঘর,0,"Meme, TikTok and others"
বাবরী মোসজিত থাকবে,0,"Meme, TikTok and others"
হায় রে হায় দুধ নাকি কি দুটো মিলে কেজিতো হবেই,0,"Meme, TikTok and others"
আল্লা যেন এই লোকটাকে নেক হায়াত দান করেন আমিন,0,"Meme, TikTok and others"
তাসলিমা নারসির এক বে ধর্মি তার মুখে কোন কথা মানায না,0,"Meme, TikTok and others"
খুনি হাসিনার ফাঁসি চাই,0,"Meme, TikTok and others"
মুদিসরকারকে পৃথিবীর জমিন থেকে সরিয়ে দেয়া হোক মোঃ নজরুল ইসলাম,0,"Meme, TikTok and others"
আসলে এখানে যদি দুই মাস ধরে তাদের বিয়ে হয়েছে আজ সে স্বামীকে বাঁচানোর জন্য স্ত্রী অবশ্য দূরে যেত সে দাঁড়িয়ে থাকতো না তার আমার যেটা বলার আমার এটার মানে বুঝতে পারতাছি আসলে এখানে বোর্ড কিছু ষড়যন্ত্র আছে যেহেতু কারণে বন্ধুরা এরকম করতে পারতাম,0,"Meme, TikTok and others"
আরে কাকু তো মেন্টাল,0,"Meme, TikTok and others"
আমি চাই দুই জন এক হয়,0,"Meme, TikTok and others"
কাশ্মীরা মোদি মোরুক🤣🤣,0,"Meme, TikTok and others"
অবশ্যই কলকরবেন,0,"Meme, TikTok and others"
আপনার বাড়ি টাংগাইল তাইনা,0,"Meme, TikTok and others"
সাকিব অপুর জুটি এক চাই,0,"Meme, TikTok and others"
ভাই আপনারাই একমাত্র লোক যারা এরকম সন্তানকে সাইজ করতে পারবেন,0,"Meme, TikTok and others"
সুখের বাজারে গিয়েছিলাম সুখ কিনার জন্য সুখের দাম বেশি ছিল তাই কিনতে পারলাম না দুংখের দাম কম ছিল তাই মন ভরে দুংখ কিনে নিয়ে আসলাম এই অভাগিনির নাম দেক সাহীন,0,"Meme, TikTok and others"
আমি যতক্ষণ ভিডিওটা দেখেছি ময়ূরী খানকির মাথার চুল এবং দুধের দিকে তাকিয়ে ছিলাম ওর ফেস এর মধ্যে একবারও তাকাইনি ম তোদের কারণে পোলাপান নষ্ট হয়,0,"Meme, TikTok and others"
কথাবার্তা প্রমান করে শালা আসলেই রাজাকার,0,"Meme, TikTok and others"
তাকে ভাল বাছিনা,0,"Meme, TikTok and others"
এই দরোনের পিক কি না দিলেনয়আমি বলব যে সাকিব ভাই য়া অপু আপা যদি ভূল করে তাহলে মাফ করেদি প্লিজএবার আপনারা আপনাদের ভূল বুঝাবুঝি মিটিয়ে নিন প্লিজ প্লিজআপনাদের জন্য না হয় আপনাদের ছেলের জন্য প্লিজ,0,"Meme, TikTok and others"
তরা খারাপ,0,"Meme, TikTok and others"
সানাই আপু আপনি ভাইরাল হবার জন্য মহিলাদের কতো নিচু স্তানে নিছেন ভাবছেন একবার,0,"Meme, TikTok and others"
ভারতের প্রধানমন্ত্রী নরেন্দ্র মোদি,0,"Meme, TikTok and others"
যতসব ফালতু খবর মিথ্যাবাদী,0,"Meme, TikTok and others"
আশাকরি অনেক ভালো লেগেছে আর শাকিব বাই অপু আপ্পিকে এক সাথেই দেখলে আমি অনেক খুসি হব দোয়া করি অপু শাকিব আর আমাদের সবার প্রিয় আব্রাম খানকে একসাথে দেখার জন্য আপনারাও কিন্তু দোয়া করবেন ধন্যবাদ সবাইকে,0,"Meme, TikTok and others"
শাহখরুফ খানকে ধ্যানবাদ,0,"Meme, TikTok and others"
আমি এই ধরনের শো গুলোর কমেন্ট পড়ে মজা পাই আপনারা আর কে কে পান,0,"Meme, TikTok and others"
আল্লাহ তুমিই ভাল জানো,0,"Meme, TikTok and others"
তোমাদেরআমরাকমেনটকরিতোমরাকথাবলনা,0,"Meme, TikTok and others"
আল্লাহ বর্তমান জামানায় জাকির নায়েক কে সত্যি প্রচার করার জন্য পাঠিয়েছেন আর যারা সত্যির দুশমন তারাই জাকির নায়েক এর বিরোধী,0,"Meme, TikTok and others"
আল্লার কচম তুই নামাজকে গালি দিলো তোর মার পুটকি দিয়ে তোরে বইরা দিমু,0,"Meme, TikTok and others"
ওকে সরির কেটে কেটে লবন ঘসে মেরে ফেলুন,0,"Meme, TikTok and others"
ওরে দইরা পিটান,0,"Meme, TikTok and others"
ময়ুরী মুনমুন কে দেখলে মনে পরে যায় থেকে পযন্ত বাংলা চলচিত্র কে যগন্য নোংরা চলোচিএ করে বাংলা সিনেমা কে দংস করে দিছে তখন সপরিবারে সাথে মানুষ সিনেমা হলে যেতে পারতো না রাস্তা ঘাডে পুষ্টার দেখলে মনে হতো নেকেট ছবি এখন সিনেমা হল গুলো গরুর খামার আর পতিতালয় ব্যবসা হয় এখন আর বাংলা চলোচিএ মানুষ দেখে না সুদু নাটক টেলি ফিল্ম ছারা,0,"Meme, TikTok and others"
ও যখন বৃদ্ধ হবে তখন তার ছেলেও এইভাবে ঠাস ঠাস করে মারবে,0,"Meme, TikTok and others"
মন্দির জিন্দাবাদ,0,"Meme, TikTok and others"
সে সঠিক বলে গেছে,0,"Meme, TikTok and others"
আবার ওকে শ্টেসনে পাঠাও,0,"Meme, TikTok and others"
এতো বড় কিভাবে,0,"Meme, TikTok and others"
বাপ কা বেটাধন্যবাদ,0,"Meme, TikTok and others"
আমরা মুসলমানদের পক্ষে,0,"Meme, TikTok and others"
এক মাএক বাবা যদি ছয় সন্তান লালন পালন করতে পারেতাহলে ছয় সন্তান কেন এক মা বাবাকে লালন পালন করতে পারে না সেটা আমার জাতির কাছে প্রশ্ন,0,"Meme, TikTok and others"
গেরাম বাসির সামনে জোতাপিটা করাদরকার,0,"Meme, TikTok and others"
ভাই আমি সাইপ্রাজ থাকি আমি এখান থেকে বিবাহ করে আসলে কি বাবে কি করতে হবে আমাকে জানাবেন কি দয়াকরে ভাই,0,"Meme, TikTok and others"
ওর ছেলে ও ওকে এভাবে মারবে একদিন এই কামনা করি,0,"Meme, TikTok and others"
শেষ পর্যন্ত বুড়ো কাকার গায়ে জুলে গেলি এরা পতিতা নামের মডেল বাগ্গিস বিনে পয়শা রপ্তানি হলো পতিতা এরকম পতিতা দেশে আরো অনেক আছে যারা যেথে ছাইবে তাদের কে বিনে পয়শায় ভিসা দেওয়া হবে,0,"Meme, TikTok and others"
পাকিস্তান এগিয়ে যাও,0,"Meme, TikTok and others"
ঝুলে আছে,0,"Meme, TikTok and others"
এই লোকটাকে জনগন মিলে মারা উচিত,0,"Meme, TikTok and others"
তালে ঠিক চালিয়ে যাও,0,"Meme, TikTok and others"
রাই মানিনা মসজিদ চাই,0,"Meme, TikTok and others"
আমি কাশঁমির,0,"Meme, TikTok and others"
ডানডির পোলা ডানডি,0,"Meme, TikTok and others"
পচা,0,"Meme, TikTok and others"
কথা গুলা কি সত্যি আপুযদি সত্যি হয় খুব বেশি খুশি হবো,0,"Meme, TikTok and others"
হ্যা ভাই আমিও যাই তারা জেনো মিলি জাই,0,"Meme, TikTok and others"
বিপক্ষ,0,"Meme, TikTok and others"
তোমারনামবারদাও,0,"Meme, TikTok and others"
আল্লাহ তুমি নাই তুমি এর বিচার কর আল্লাহ,0,"Meme, TikTok and others"
মিথ্যা প্রচার কর আপনারা কয় টাকা পানএই দালালি করে কত টাকা পানসব ফাল্তু তথ্য প্রচার করতে আপনার লজ্জা করেনা,0,"Meme, TikTok and others"
ওর ফাসি হওয়া উচিত ছিল ছিঃ ছিঃ বাবার গায়ে হাত,0,"Meme, TikTok and others"
আমি মুছলিম এর পককে আছি জয় হবে পাকিছতানের আললাহ আছেন,0,"Meme, TikTok and others"
অই ছেলেকেফাসি দেউয়া দরকার,0,"Meme, TikTok and others"
দেত বাজে নিউজ,0,"Meme, TikTok and others"
ওরে দুধ গুলো যদি চুষতে পারতাম,0,"Meme, TikTok and others"
বাবাটা কি বেচে আছে এই ছেলের বাচার কোন অধিকার নাই একে এমন শাস্তি দেওয়া উচিত যাতে আর কোন ছেলে বাবা মার সাথে এমন কাজ করার সাহস না পাই,0,"Meme, TikTok and others"
এটা ছেলে নামে কল্কই,0,"Meme, TikTok and others"
মুসলমান মানে আতঙ্ক বাদি,0,"Meme, TikTok and others"
বাংলাদেশের নায়ক নায়িকাদের দেখলেই হাসি লাগে সিনেমার ভিতর কি বলে আমি কিছুই বুজতে পারি না সিনেমা করে নাকি পালা গান করে ভাই বোঝা বড় মুশকিল,0,"Meme, TikTok and others"
আমি আছি তোমার নাম্বার দাও,0,"Meme, TikTok and others"
পিডা,0,"Meme, TikTok and others"
হে ঈশ্বর তুমি কোথায়,0,"Meme, TikTok and others"
মেয় ছাই ইমু,0,"Meme, TikTok and others"
এত বড় দেশ ইন্ডিয়া আর মন্দির বানানোর জন্য এই মসজিদের জাগাটাই প্রয়োজন হিংসাবিদ্বেষ বাদ দিয়ে যার যার ধর্ম সে পালন করাই ভালো,0,"Meme, TikTok and others"
বস্ সবার সেরা,0,"Meme, TikTok and others"
আমি করিম ডাকাত বলছি ওর ঠিকানাটা বল বেন ভাইরা বিনা টাকায় মাডার করবো পুলিশ কিছুদিনের জন্য জেল খাটিয়ে আবার ছেড়ে দেবে ফাঁসি দেওয়া আর মাডার করা নামমৃত্যু নাম্বার,0,"Meme, TikTok and others"
এই রাই হিন্দু র পক্ষে বিজেপি সরকারের রাই হিন্দু ত বাদি রাই আমি মনে করি,0,"Meme, TikTok and others"
সাকিব খােনর উপর খোদার গজব প রুক,0,"Meme, TikTok and others"
আপু আপনি বিয়েকরেছেন না করলে বলবেন,0,"Meme, TikTok and others"
শাকিব খান কে কেনো টানোস পূর্নিমা,0,"Meme, TikTok and others"
ভাই আমার মনে হয়েছিলো জে সিফাত ওই ভাবে বলতে চাইনাই জে নামাজ নিয়ে কথা বল্লেতে,0,"Meme, TikTok and others"
ওর ফাঁসি চাই ফাঁসি চাই,0,"Meme, TikTok and others"
ফালতু ভিডিও ছাড়া বাদ দেন শিরোনাম হচ্ছে একটা আর গল্প হচ্ছে আরেকটা এটা কি ধরনের বাজে ভিডিও ধোকাবাজ,0,"Meme, TikTok and others"
আসলে রানু দিদি কি বলতে চেয়েছে তা বুঝতে পারেনি আমার মনে হয় তাকে ক্ষমা ক্ষমা করে দেওয়া উচিত,0,"Meme, TikTok and others"
একটা কমেন্টও বাপ্পির পক্ষে পাওয়া জাচ্ছেনা তার পরও এটা হিরো কিভাবে হলো,0,"Meme, TikTok and others"
কত টাকা লাগবে,0,"Meme, TikTok and others"
ভাই কোথায় পাবো এই লোকে,0,"Meme, TikTok and others"
সারুকভাইকে ধনৃবাদ সতৃকথাবলারজনৃ অাললাহ অাপনাকেনেক হায়াতদানকরেন,0,"Meme, TikTok and others"
কোন বাবাকে পিটাচ্ছিস বেয়াদব তোকে কোলে তুলে কত আদর করেছে,0,"Meme, TikTok and others"
ওকে গুলি মারা ওচিত,0,"Meme, TikTok and others"
কাসম্মির,0,"Meme, TikTok and others"
মময়াহগড,0,"Meme, TikTok and others"
আল্লাহ আপনাকে হেদায়েত করুন,0,"Meme, TikTok and others"
নারায়ে তকবিরআল্লাহু আকবার,0,"Meme, TikTok and others"
বাংলা দেশে ও তো ছেলে দের কে টাকা দিয়ে যৌন সুখ নিতে হয়,0,"Meme, TikTok and others"
মুসলিমরা নতুন একটি দল করা হক ভয় কিসের,0,"Meme, TikTok and others"
আপনারাই তো তাকে খোঁচা দিয়ে দুই পয়সা কামাওঅতিন্দরনাথ তোমাদের মত না যে গল্প শুনাচ্ছ,0,"Meme, TikTok and others"
শাকিব খান অপু বিশ্বাস কি মিলে নিন,0,"Meme, TikTok and others"
এই বিয়েটাও বেশীদিন টিকবেনা,0,"Meme, TikTok and others"
তুমি ভাই একটা ফালতু লোক আছো,0,"Meme, TikTok and others"
আচুদা ক্যাপশন একটা দিয়ে রাখছে,0,"Meme, TikTok and others"
আমারা পাকিস্তানের পক্ষে কাশ্মীর সাধীন চায়,0,"Meme, TikTok and others"
সাকিব খান ও অপু বিশাস আপনারা দুই জন্য এক সাতে থাকুন,0,"Meme, TikTok and others"
অকে মেরে ফেলা হোক এক সাতে ওনার ছেলের বউ কে পালিস মেন দেয়ার দরকার ছেলের বউ তামাসা দেখছে শসুরকে মারছে,0,"Meme, TikTok and others"
বাপ্পির সাতে অপুকে চাইনা বাপ্পি অপুর ছেলের মতো অপুর সাতে জায়না,0,"Meme, TikTok and others"
আল্লাহ তুমি কোথায় আছ আমি এই জানুয়ার কে পেলে জুতা ঝাড়ু দিয়ে পিটিয়ে লম্বা করতাম আছে কপালে তুর ও তুর ছেলের হাতের তুই খাবি,0,"Meme, TikTok and others"
আললাহ তায়ালা জেন সাকিব ভাই ওঅপু আপুকে জেন এক করে দেয়,0,"Meme, TikTok and others"
পাকিস্তান জিন্দাবাদ ইন্ডিয়া ধংস হোক,0,"Meme, TikTok and others"
ভিডিও চাই নইলে ফেক নিউজ,0,"Meme, TikTok and others"
এটা মানুষের কাজ না,0,"Meme, TikTok and others"
ম্নবভ,0,"Meme, TikTok and others"
ওকে ফাসি দেওয়ার দরকার ওকে কমা করা যাবেনা,0,"Meme, TikTok and others"
ওর বাবাকে মারা প্রত্যেকটা চড় আমার কলিজা তে গিয়ে লাগতেছিলওরে আর ওর বউ কে পৃথিবীর সবচেয়ে কঠিন শাস্তি দেয়া হউক,0,"Meme, TikTok and others"
শাকিবের চবি আর বচর করতে পারবে,0,"Meme, TikTok and others"
রানু দি আসলে জানেনা দূত এবং চাকরের মধ্যে পার্থক্য এই রকম মানুষ আসলে অনেক সরল ওটা কারো শিখানো কথা ছিল অতীন্দ্র সেটা খুব ভালো ভাবে জানে বলে এই ভাবে যে উপরে উঠে আসে সে কোনো দিনের জন্য অসম্মান করতে পারে না অশিক্ষিত মানুষ কথা বলতে ভুল হতে পারে একা তার কাছে গল্প করুন বুঝতে পড়বে অন্তরের ভালো বাসা,0,"Meme, TikTok and others"
আমার কবিত,0,"Meme, TikTok and others"
আরে জানোয়ারের বাচ্চারে,0,"Meme, TikTok and others"
বালের নিয়ুজ,0,"Meme, TikTok and others"
পাকিস্তান আামাদের শত্রু ওরা বাংলাদেশকে শোষণের পর শোষণ করেছে,0,"Meme, TikTok and others"
ফরিদপুরের মেয়েরা কি তোমারে ভাটিকেল মারছে,0,"Meme, TikTok and others"
যে বাবা খাওয়াই মহিষের মতো মোটা করল ছেলেকে সেই ছেলেই এভাবে বাবাকে মারল চোখে পানি চলে আসে এই মহিষটার হাত পা কেটে দেয়া উচিত অথবা গণপিটুনিতে মেরে ফেলা যায় বাংলাদেশে এমন ঘটনা ঘটলে গণপিটুনিতে মারা যেতো,0,"Meme, TikTok and others"
সাকিব খান ঠিক বলেছে,0,"Meme, TikTok and others"
বাজে ভিডিওচটি পিসির পা চাটার জন্য কত টাকা নিয়েছেন ওকে মুখ্যমন্ত্রী করে খুব বড়ো ভুল করেছে পশ্চিমবঙ্গের মানুষ সাম্প্রদায়িক নিয়ে কথা বলে উনি বিজেপি কে দোষারোপ করেন কিন্তু সবথেকে বড়ো সাম্প্রদায়িক রাজনীতি করছেন মমতা বন্দ্যোপাধ্যায়,0,"Meme, TikTok and others"
ওর মতো শয়তানের ফাঁসি চাই,0,"Meme, TikTok and others"
এবার যাবি কোথায়,0,"Meme, TikTok and others"
মুজিত আমি চাই,0,"Meme, TikTok and others"
বাবাকে মারা অপমান করা মোটেই ঠিকনা তবে এখন ছেলের কামাই রুজগার দিয়া সাংসার চলে সেই ছেলেকে জেলখানায় না দিয়ে বাড়িতেই পিটন দেওয়াই ভালো হবে কারন সে টাকা রোজগার না করতে পারলে বাবা মা না খেয়ে থাকলে আরো খারাপ,0,"Meme, TikTok and others"
একজন মজাদার মানুষখুব ভাল লাগে,0,"Meme, TikTok and others"
তুমি এসে রাজ নিতিকরো,0,"Meme, TikTok and others"
এই তুই বেস্যা মিথ্য কথা বলছিস,0,"Meme, TikTok and others"
ওকে তো পৃথীবির আলো দেখার আগেই মেরে ফেলা উচিত ছিল এই ছেলে মা বাবার পপের ফল,0,"Meme, TikTok and others"
সেফাত হলো নাস্তিক এই হলো একটা ফালতু লোক একে পেলে অনেক লোকেই মারবে,0,"Meme, TikTok and others"
আমি কাশ্মীরের জনগনকে সমর্থন জানাই এর মানে পাকিস্তান কে সার্পোট করি মুসলমানদের বন্ধু পাকিস্তান মালেশিয়া তুরস্ক ইরান ইন্দোনেশিয়া আর কাফের হলো সৌদি মিশর আমিরাত বাহারাইন,0,"Meme, TikTok and others"
অরে রড দিয়া মাইরা হাত ভেঙে দেয়া উচিত,0,"Meme, TikTok and others"
কি সোনা এভাবে কেউ বলে তুমি কিভাবে টাকায় করেছ তুমি তো টাকায় করেছ নিচের তলা বিক্রি করে নাই ভাড়া দিয়ে উপর তলা করেছে তুমি জানো না তুমি খুব ভালো মেয়ে না ঐ কারণে যে তুমি দুধ বিক্রি করে নিচের তলা ভাড়া দিয়ে তোমার টাকা আই করেছ ছি ছি ছি,0,"Meme, TikTok and others"
ওর ফাঁসি চাই বাবারে মারে বেয়াদব,0,"Meme, TikTok and others"
বাবা মা কতো কষ্ট করে নিজের সন্তান কে মানুষ করেআর সেই ছেলে যদি হয় অমানুষ এর চেয়ে পোরা কপাল আর কি হয়,0,"Meme, TikTok and others"
সব বুড়ো গো ভাল লাগে মিথিলার,0,"Meme, TikTok and others"
ঐ ব্যাক্তি চাকরি করে মানে ও শিক্ষিত এ কেমন শিক্ষা ওর মতো শিক্ষিত জানোয়ারের কোন প্রয়োজন নেই মেরে ফেলা ভালো,0,"Meme, TikTok and others"
আপনার এত নোংরা চিনতা কেনো,0,"Meme, TikTok and others"
জাকির নায়েকের ব্যাপারে আপনি যে শব্দ গুলো ব্যবহার করেছেন তা অত্যন্ত ন্যাক্কার জনক,0,"Meme, TikTok and others"
ওকে জুতা পিটা করতে হবে মেয়ে নামে কলংক এইজন্য উপকার করতে নেই,0,"Meme, TikTok and others"
মোদী একটা জাহেলের বাচ্চা,0,"Meme, TikTok and others"
এমন নায়ক কয়েকখানা হলে দেশে আর কিছুর প্রয়োজন নাই,0,"Meme, TikTok and others"
ব,0,"Meme, TikTok and others"
শয়তান,0,"Meme, TikTok and others"
আমি সবার আগে কমেন্ট পরি তার পরে দেখি আসলে ওর কোন লচ্চা নাই বুকে কাপর দিতে পার না মাগি,0,"Meme, TikTok and others"
কোলকাতা ইন্ডিয়া তেই এ সব সম্ভব কারণ ওদের মতো এত ছোট মন মানুষিকতা আর কথাও নেই,0,"Meme, TikTok and others"
খারাপ তা শুনতে চাই,0,"Meme, TikTok and others"
জে টা বিয়ে করে সে তে প্রতি দিন করে,0,"Meme, TikTok and others"
আল্লাহএ কি সময় এলো,0,"Meme, TikTok and others"
আমি নিরাপদে আছি,0,"Meme, TikTok and others"
রানু একটা আমার কথায় একমথ হলে লাইক করো,0,"Meme, TikTok and others"
বাপরে একশো,0,"Meme, TikTok and others"
মনটা শান্তি হলো,0,"Meme, TikTok and others"
আরে তোরা এলাহাবাদ হাইকোটে#,0,"Meme, TikTok and others"
বাংলাদেশের টিভি চ্যানেল গুলোতে যেই হেলথ টিপস অনুষ্ঠান হয় ঐখান থেকে জনগনের খুব একটা উপকার হয় বলে আমার মনে হয়না এদের অনুষ্ঠানে বেশীরভাগ ক্ষেত্রে ধানদবাজীর গন্ধ থাকেআর মেডিকেল ভাষায় কথা বলে জনগন কে বিভ্রান্তি করে,0,"Meme, TikTok and others"
আমার একজন ভাবি বা মেয়ে দরকার,0,"Meme, TikTok and others"
আমার প্রশ্ন আপ্নে কতজনের সায়ে সেক্স কতেছেন,0,"Meme, TikTok and others"
এসি ঘটনা আমাদের দেশে নয় এটা পচ্চিম বংগে,0,"Meme, TikTok and others"
ছি ছি,0,"Meme, TikTok and others"
মোদি বাদিদের ধংস করে দাও,0,"Meme, TikTok and others"
কাশ্মীর জয় হবে,0,"Meme, TikTok and others"
যারা বিনা অপরাধী নারী শিশু ও মানুষকে অত্যাচার হত্যা করছে তারা তো পশু,0,"Meme, TikTok and others"
জাহারনাম নামে জাবে এরা,0,"Meme, TikTok and others"
মুসলিম ভাই সব এক হ‌ও ইনসাআল্লাহ বাবরি মসজিদ ফেরত পাবো,0,"Meme, TikTok and others"
আগে তো ময়রি লেংটা ছবির নাইকা ছিলো আলেক জান্ডার বো অরে দুধ টিপছে এখন দেখা যাইতাছে দুধ বর বেশি ছিছিছি,0,"Meme, TikTok and others"
আপনার হিংসা হয়,0,"Meme, TikTok and others"
ত্রমপির ছেলেকে ধরছেনা কেন পুলিশ ভাইয়েরা,0,"Meme, TikTok and others"
দেখলাম ভিডিও টা হোক না হিন্দু কান্না ধরে রাখতে পারিনি,0,"Meme, TikTok and others"
জানোয়ার,0,"Meme, TikTok and others"
কোন নায়িকা বলতে পারবে সে যৌন কর্মী না,0,"Meme, TikTok and others"
প্রতিবেশীকে ধন্যবাদ জানাই,0,"Meme, TikTok and others"
সানাই তেকে বেসি আছে,0,"Meme, TikTok and others"
আমিও চাই এক হয়ে যায়,0,"Meme, TikTok and others"
বাপ্পী শাকিবকে কপি করে সর স্টাইল বলদানায়ক,0,"Meme, TikTok and others"
আপনার নামবারটা দিবেন কথা বলব,0,"Meme, TikTok and others"
এতোদিন মেয়ে কোথায় ছিলো,0,"Meme, TikTok and others"
আপনি কি ছিলেন ওখানে,0,"Meme, TikTok and others"
এটা কে মইরি নাকি,0,"Meme, TikTok and others"
তুমি যে প্রচার করো শুধু মুসলিম নিয়ে প্রচার করলেই হবে,0,"Meme, TikTok and others"
কাকু তুমি আছছা একটা লুচ্ছা,0,"Meme, TikTok and others"
মদি ঝড়ের মতো এসেছিল ঝড়ের মতো যাবে কেই রুখতে পারবে নাও যা টাকা মেরেচে ওর পুরুষ বসে খাবে,0,"Meme, TikTok and others"
তোমার নাম্বার টা দেও,0,"Meme, TikTok and others"
মিথ্যা পোচার করা আপনারা ছাড়ূন তো যত সব ফালতু কথা,0,"Meme, TikTok and others"
এর পক্ষে,0,"Meme, TikTok and others"
শান্তি চাই,0,"Meme, TikTok and others"
এই ছেলেটা কে কঠোর শাস্তি দাবি জানাই যা দেখে আর কোনো ছেলে তাদের বাবা মাকে আগাত করতে না পারে,0,"Meme, TikTok and others"
আমি এর বিপক্ষে,0,"Meme, TikTok and others"
এইসব বাঙালির কাজই হচ্ছে যেকোনো মানুষের সম্পর্কে কিছু না জেনে শুধু উল্টা পাল্টা কমেন্ট করা আর কে কে আমার সাথে একমত,0,"Meme, TikTok and others"
ভারত সরকার ও জিতবে,0,"Meme, TikTok and others"
আরে সাকিব তো একটা লুচ্চা,0,"Meme, TikTok and others"
আল্লাহ তুমি এই মানুষ রুপি জানয়ার এর বিচার করো,0,"Meme, TikTok and others"
কুমিল্লা কই,0,"Meme, TikTok and others"
ভাল হিন্দুরা প্রতিবাদ করছে,0,"Meme, TikTok and others"
সাংবাদিক আপু কি শোনালেন আমি কান্না ধরে রাখতে পারছিনা উনি হলেন সেই নেতা যার কাছে ভয় ও হার মানতো,0,"Meme, TikTok and others"
এটা কি অামেরিকান গাবি নাকি,0,"Meme, TikTok and others"
খুবই সময়উপযোগী,0,"Meme, TikTok and others"
এই রেশমি তোর বাড়ি কোথায়,0,"Meme, TikTok and others"
উত্তর প্রদেশের মন্ত্রী এই হালার মাথা অপারেশন করার জরুর এই শীতের কালে মানুষের জাগে না কিনে দিয়ে গরুর যা গেট কিনে দিচ্ছে এই হালা গরু উনি একটা জাগে লাগাও,0,"Meme, TikTok and others"
মদিহলোসয়তানেরবাচ্চা,0,"Meme, TikTok and others"
জানোয়ার রে যেন ফাসি দেওয়া হয়,0,"Meme, TikTok and others"
আমি আজও বলছি আমি কোন দেশের পক্ষেনাতবে আমি সন্ত্রাসীর বিপক্ষে আর আমার মতে মৌদি শান্তি বিনষ্টকারি একজন সন্ত্রাসী কারন মুসলিমরা কখনো শান্তি বিনষ্ট কারির পক্ষেনাআর মৌদি জমানায়গোটা দক্ষিণ এশিয়ায় মুসলিম বিদ্দেশি সড়যন্ত সৃষ্টি হচ্ছে আর এর পিছনের নাটের গুরু যেমন কুখ্যাত ভার্মিজদের উস্কানি দিয়েছে এই সন্ত্রাসী মৌদি আমাদের গৌটা বাংলাদেশ জিম্মি হয়ে আছে এই মৌদিদের উস্কানিতেগৌটা ভারতে মুসলিম হত্যা নির্জ্যাতন হচ্ছে এই কুখ্যাত মৌদির ইংগিতেআর আসুন কাশ্মীরের ব্যপারে যেহেতু কাশ্মীর আগে ভারতীয় কোন অংশ ছিলোনা একটা রাজ্য চিলোএবং দ্বারা মেনে নিয়েই ভারত কাশ্মীরিদের তাদের সঙ্গে নিয়েছে তাই দ্বারা একটা চুক্তি চিলো এখন ভারত দ্বারা বিলুপ্ত করা মানেই চুক্তি ভঙ্গ করা আর চুক্তি ভঙ্গ করা মানে কাশ্মীর তাদের আগের রাজ্যে পিরে যাওয়া এবং দ্বারা বিলুপ্ত করার পর কাশ্মীরে ভারতের কোন অধিকার থাকতে পারেনা ঐ দ্বারা বাতিলের সাথে সাথেই কাশ্মীরে ভারতের অধিকার বিলুপ্ত হয়েছেতাই ভারত এখন কাশ্মীরে ডুকাই সন্ত্রাসী কার্যকলাপ চাড়া আর কিছু নাএবং কাশ্মীরে ভারতীয় সেনাবাহিনী এখন কাশ্মীরিদের কাছে সেনাবাহিনীনা সন্ত্রাসী দখলদার হানাদার বাহিনী হিসেবে বিবেচ্ছ তাই এর জন্য সর্ব প্রথম এগিয়ে আসার প্রয়োজন চিলো জাতীয় সংঘকে এগিয়ে আসার প্রয়োজন চিলো কিন্তু আসেনাই আর না আসার একটাই কারণ জাতীয় সংঘকে কিছু ধানবীয় রাষ্ট্র দুর্বলের জন্য অন্ধ সংঘ বানিয়ে রাখা হয়েছে যার কারনেই জাতীয় সংঘ দুর্বলদের উপর অত্যাচার দেখেনাতাই আজ এই নির্জ্যাতিত কাশ্মীরিদের পাকিস্তান নয় যেইকোন সভ্য রাষ্ট্র এগিয়ে এসে হানাদার মৌদি বাহিনীদের প্রতিহত করাই হবে উওম এবং সভ্যতার প্ররিচয় দেওয়া বীর জাতির প্ররিচয় দেওয়াকারন মৌদির কার্যকলাপে বুযা যাচ্ছে এই মৌদি ইসরাইলের চেয়ে ভয়ংকর এক ধানব,0,"Meme, TikTok and others"
হিন্দুদের ধর্ম তে এটা বিদ্য মা বাবা ওপর হাত উঠানো,0,"Meme, TikTok and others"
স্টার জলসা,0,"Meme, TikTok and others"
এর বিচার হওয়া উচিত,0,"Meme, TikTok and others"
দুজনএকহয়,0,"Meme, TikTok and others"
ভাল আছনি অপু সাকিব,0,"Meme, TikTok and others"
আমি ও চাই অপু ♡ শাকিব,0,"Meme, TikTok and others"
এই ফালতু কই পাও তোমরা মিথ্যা যত বানোয়াট,0,"Meme, TikTok and others"
আমি যাবো,0,"Meme, TikTok and others"
মোদী গনহত্যা বন্ধ কর,0,"Meme, TikTok and others"
নিরদস সে আমাদের নেয়ামত,0,"Meme, TikTok and others"
ভাল লাগেছে,0,"Meme, TikTok and others"
বাহ আবার মা ডাকে মা শব্দ তোদের মতো অমানুষের জন্য না আর যে বউ সামনে দাড়ায় সব দেখলো তরেও যে আল্লাহ কেমন সন্তান দিবে আল্লাহ ভালো জানে আল্লাহ এমন সন্তানের থেকে সন্তান না হওয়া ভালো,0,"Meme, TikTok and others"
মান্না ভাইয়ের অকাল মৃত্যুতে আজ বাংলা চলচিত্র অঙ্গনে অনেকেই বড় বড় কথা বলছে মান্না ভাইয়ের অকাল মৃত্যুতে আজ অনেকেই চলচিত্রে ছবি করার সুযোগ পাচ্ছে,0,"Meme, TikTok and others"
ইফতারের পার্টি তে আসা হয় কিএক্টাবস্থা,0,"Meme, TikTok and others"
সাকিব খান সব ছবি দেখতে চাই সাকিব খান কিং খান নাম্বার সাকিব খান,0,"Meme, TikTok and others"
অশিক্ষিত অর্ধশিক্ষিত আর প্রবাসী অল্পশিক্ষিতদের দারাই এতো সুন্দর এবং খুবই গুরুত্বপূর্ন একটা বিষয় নিয়ে গালাগালি হাসিঠাট্টা করা সম্ভব এই আবাল মার্কাগুলোর জন্যই দেশটার নারী সমাজ এখনো এগুতে পারছে নাহ প্রবাসী গুলো বেশিরভাগই থাকে যেখানে নারীর সামাজিক অধিকার প্রায় নেই বললেই চলে তাই তাদের নারীদের ব্যপারে চিন্তা ভাবনা অনেক নিচু মানের হয়ে যায়,0,"Meme, TikTok and others"
রিয়াল সেক্স করবা,0,"Meme, TikTok and others"
তোর বাবা মোদিকে জেলের ভাত খাওয়াবে নাকি,0,"Meme, TikTok and others"
লোভে পাপ আর পাপে মৃত্যু এই রানুর ও একদিন এই অবস্থা হবেখুব বাজে এই রানুদি,0,"Meme, TikTok and others"
মোমোতার কাছে অনুরোধ অকে ফাঁসি দেওয়া হোক সবাই সাড়া তোলো,0,"Meme, TikTok and others"
এই বেয়াদবকে চাকরি দিছে কে ওর কোনো জগ্যতাই নেই গালি দিলাম না তবে ওর কঠিন শাস্তি হওয়া উচিত,0,"Meme, TikTok and others"
কাশ্মীরে পক্ষে,0,"Meme, TikTok and others"
প,0,"Meme, TikTok and others"
কোথাকার ঘটনা,0,"Meme, TikTok and others"
অতিমরায টাকার লোব থাকতে পারলেন না টাকার লোভে যদি থাকতে পার্থ তাহলে এইরাম করে একটা ইন্টারভিউ এর জন্য কত টাকা চাইতো না গরিব হয়ে বড় জায়গায় টাকার অংকটা বেশি হয় জয় এইসব গরিব মানুষের ওসব জায়গায়,0,"Meme, TikTok and others"
কিছু বলার ভাষা পাচ্ছিনা শুধু মিষ্টি খাওয়ার জন্য এভাবে বৃদ্ধ বাবাকে এভাবে মারতে পারে ছেলেকে ফাসি চাই,0,"Meme, TikTok and others"
কথায় আছেনা যখন তোমার কেউ ছিলনা তখন ছিলাম আমি এখন তোমার সব হয়েছে পর হয়েছি আমি রানুর মেয়েএত দিন কোথায় ছিল যখন তার মা রাস্থায় পরে থাকতো না খেয়ে অনাহারে কারো না কারো উছিলায় সৃস্টি কর্তা মানুষকে উচ্ছসিড়িতে পৌছে দেয়রানুর ব্যাপারটা তেমনি অতিন্দ্রতপনতাদের উছিলায় রানু এখন বড় সেলিব্রিটি সারা বছরেও যদি রানুমন্ডলের একটি গানের পয়সা অতিন্দ্র তপন কে দেওয়া হয় তার পরেও তাদের উপকারের কথা রানুমন্ডল শেষ করতে পারবে না,0,"Meme, TikTok and others"
বিল পাশ করানোর দরকার,0,"Meme, TikTok and others"
এখনো সময় আছে তাওবা করে ভাল হয়ে যাও মরনের পরে তোমাদেরকে জাহান্নামের লাকড়ি বানাবে,0,"Meme, TikTok and others"
আলহামদুলিল্লাহ্ আমরা অনেক খুশি হলাম দোয়া ও শুভ কামনা রইল,0,"Meme, TikTok and others"
এটাতো মেয়ে দের পায়না আর কি করতে পারে একটা মেয়ে কতা টাকস্টেপরেও সুখের মুখ দেকতে চায় একটা মেয়ে,0,"Meme, TikTok and others"
কি যে হবে দেশের অবস্থা সবাই লাগানো নিয়ে ব্যাস্ত আর ওই সব ছবি,0,"Meme, TikTok and others"
ভাইয়া আপনি যে তিনটা রাশি বললেন নামের আগে কোন অক্ষর হয়,0,"Meme, TikTok and others"
আমরা চাই আপু শাকিবের বউ হয়ে থাকুক,0,"Meme, TikTok and others"
আল্লাহ এই নরপিশাচের বিচার কর,0,"Meme, TikTok and others"
বিএনপি ক্ষমতায় আসলে ময়ুরীরা আবার তাদের সেই ফিল্মগুলোর মতন আরো ফিল্ম সবাই দেখতে পাবে,0,"Meme, TikTok and others"
ওমানুষ ওকে কঠিন শাস্তি দেয়া উচিত,0,"Meme, TikTok and others"
উনি কি বাংলাদেশর অভিনেতা বুঝলাম না,0,"Meme, TikTok and others"
লম্পট চরিত্রের লোক শাকিব,0,"Meme, TikTok and others"
সবাই একটি বিষয় নিয়ে খারাপ মন্তব্য করেছে যেটা মোটেও ঠিক নয় কারণ যে যত খারাপ তার চিন্তাভাবনা ঠিক তেমনি হবে এই নায়িকা এখন সাংসারিক ও সালে অভিনয় ছেড়ে দিয়েছে ও পরেও মনে হয় টি ছবিতে অভিনয় করেছে আমরা সংযমী হতে শিখি,0,"Meme, TikTok and others"
জবাই করা উচিত এমন ছেলেকে,0,"Meme, TikTok and others"
পাকিল্কস্টানজংগীনাভালো,0,"Meme, TikTok and others"
সারাদিন কাজ করেরুমের মধ্যে এসে একটু ইউটিউব দেখতেছিলামকিন্তু এটা দেখে কিছু বলার মত নাইকষ্টটা আরো বেরে গেলো,0,"Meme, TikTok and others"
আমরাও চাইজে মেনে নিক,0,"Meme, TikTok and others"
এই রকম অমানুষ জনম না দিয়ে কুকুর পালা উচিৎ কুকুর মালিককে কামড় দেই না,0,"Meme, TikTok and others"
পাগল পাগল থাকে,0,"Meme, TikTok and others"
মিথ্যুক,0,"Meme, TikTok and others"
ওকে বহিস কার করার জন্য ধন্যবাদ পরিচালক দের,0,"Meme, TikTok and others"
তুমি কি ভাবে জানো মিন্নির সাথে নয়নের সম্পর্ক ছিল আরে অপদার্থ মেয়ে তোর চ্যানেলে কমেন্ট লাইক সাবস্ক্রাইব করার জন্য তুই এই ধরনের বানিয়ে বানিয়ে উদ্দেশ্যমূলক খুনি কে বাঁচানোর জন্য ভিডিও করার কি দরকার ছিল তোদের মত কিছু জারজ সন্তানদের কারণে বাংলাদেশের আছ বড় বড় খুনিরা খুনি করে রেহাই পেয়ে যায়,0,"Meme, TikTok and others"
বেয়াদব ছেলে এরকম ছেলে থাকার চেয়ে মরায় ভালো অর মৃত্যু দন্ড দেওয়া উচিত,0,"Meme, TikTok and others"
এই ক্ষবিশের কাছে যাঁরা জায় তারা আরো আরেক বড় ক্ষবিশ,0,"Meme, TikTok and others"
জুতা পেটা করা দরকার,0,"Meme, TikTok and others"
কাশ্মীরের স্বাধীনতার পক্ষে,0,"Meme, TikTok and others"
এডমিন সাহেব নিজের চরিএ টার দিকে খেয়াল রাখুন অন্যের মাথা কাটা ছবি দিয়ে নোংরামী করবেন না,0,"Meme, TikTok and others"
আমি তোমার শূুত কথা বোলতে চাই তোমাট নামবার পাটঠ,0,"Meme, TikTok and others"
কে বলছি এই ভিডিও ডিলিট করে দেন এটা মিথ্যা সংবাদ ড জাকির নায়েক মালোয়েশিয়াতে খুব ভালো অাছেন,0,"Meme, TikTok and others"
ক্ষমা না করাই উচিত রাস্তার কুকুর রাস্তায় ভালো,0,"Meme, TikTok and others"
জবার সাথে কথা বলার উপাই বলতে পারেনসব কিছু তো বলতে পারেনতো এটা বলেন,0,"Meme, TikTok and others"
আমার একজন সুন্দরি ভাবি দরকার ফোন,0,"Meme, TikTok and others"
ভারত মুসলিম রাষ্ট্র হবে ইনশাআল্লাহ পক্ষ বুঝিনা,0,"Meme, TikTok and others"
সাকিব খান অপু খান জয় খান কে ধন্যবাদ,0,"Meme, TikTok and others"
চৈতালি রায় কলকাতা বললেও এটি ছদ্মনাম খবরের ভাষা সেটাই বলে তুরস্ক ও ইরান যদি ভারতের মুসলিমদের পক্ষ নেয় তবে বিজেপির হিন্দু জাতীয়তাবাদ সঠিক মধ্যপ্রাচ্যের অর্থায়নে পরিচালিত কিছু ভারতীয় মুসলিম মৌলবাদী সংগঠন যারা অনুপ্রবেশকারী মুসলমানদের দিয়ে ভারতের জনবিন্যাসে পরিবর্তন ঘটাতে সক্রিয় ও সবুজ ইসলামী বিশ্বের এজেন্ডা বাস্তবায়ন করছে বর্তমান সহিংসতা তারাই ঘটাচ্ছে ভারত সরকারকে এইসব মুসলিম মৌলবাদী সংগঠনগুলোর বিষয়ে কঠোর হতে হবে,0,"Meme, TikTok and others"
পুরো ভুল খবর,0,"Meme, TikTok and others"
এটা ঠিক নয় শাকিব খান অপু বিশ্বাসকে ডিভশ দিয়ে,0,"Meme, TikTok and others"
ভারত এখন আর গনতান্ত্রিক রাস্ট নয় ভারত এখন হিন্দু জঙ্গিবাদী রাস্টযাহা বিশ্বের জন্য বড় হুমকি,0,"Meme, TikTok and others"
আমি দিনে রাতে ঘন্টা ঘুমায়,0,"Meme, TikTok and others"
এর কথা আমার মোটেই ভালো লাগেনি কারন শিলপি হলো যেকোনো মানোশের মনে ভালোবাসা সিশটি করার একজন কারিকর আর যে মানোশের মনে দোখঁখ দেই সে কোনদিন শিলপি হতে পারেনা ওকে আগের যায়গায় পাঠিয়ে দেন,0,"Meme, TikTok and others"
নাউজুবিল্লাহ নাউজুবিল্লাহ,0,"Meme, TikTok and others"
বেয়াদপ তো ঐমহিলা না বেয়াদপ তুই,0,"Meme, TikTok and others"
তুই কথা যেহুত বাংলা বললি তুইত বাংগালী হেতের গুলি না দেখাইয়া তর গুলি কত বড় সেটা দেখাইলেইত পারতি,0,"Meme, TikTok and others"
সুন্দর আলোচনা এসব বিষয় সবার জানা থাকা ভালোএসব বিষয়ে আরো খুলামেলা এবং সর্বজনিন আলোচনার দরকারআমরা বাংলাদেশিরা একনো মূর্খতার চরম অবস্তানে রয়ে গেছি,0,"Meme, TikTok and others"
কাশ্মীর আমার ভাই ভারত আমার শত্রু,0,"Meme, TikTok and others"
আগে জানলে দেখতাম না,0,"Meme, TikTok and others"
গত বছরে ভারতবর্ষে মুসলমানরা হিন্দুত্ববাদী বর্বর জঙ্গিদের সাম্প্রদায়িক হিংস্রতার শিকার হয়েছে প্রায় হাজার বারেরও বেশি যা পৃথিবীর ইতিহাসে আর কোন দেশে দেখা যায় না,0,"Meme, TikTok and others"
আল্লাহুআকবার,0,"Meme, TikTok and others"
ঠিকই আচে সালারে পুলিসে ধোলাই দিক ওতো রিজই এইভাবে বাবাকে মরে মনে হচ্চে,0,"Meme, TikTok and others"
আপু আপনিতো বলেছিলেন একতলা ভারাদিয়ে দুইতালাকরেছেন আপনারনিচতালা কেমন,0,"Meme, TikTok and others"
দিদি তো সত্য ফাঁস করে দিলেন🤣🤣🤣,0,"Meme, TikTok and others"
বাল গুলো আল বাল খবোর কেন ছড়াস,0,"Meme, TikTok and others"
জয় শ্রী রাম,0,"Meme, TikTok and others"
শাকিব খান সঠিক বলেছে,0,"Meme, TikTok and others"
যখন ওরা একসাথে ছিলো তখন কি আপনিও সাথে ছিলেন,0,"Meme, TikTok and others"
আল্লাহ সবাইকে হেদায়ত করুক আমিন আল্লাহ এর নিকট সব চেয়ে প্রিয় আমল নামাজ আদায় করা পিতামাতার প্রতি সদাচরণ নামাজ আল্লাহ এর প্রতি কৃতজ্ঞতা সদাচরণ পিতামাতার প্রতি কৃতজ্ঞতা,0,"Meme, TikTok and others"
এরা মুসলিম হলে আজকে এই ভাবে কথা বলতে পারতো নাআসলে এদের বাবা মার কারনে এরা এমন অশ্লীল,0,"Meme, TikTok and others"
এগুলো করে টাকা আয় করার চেয়ে ভিক্ষা করে খাওয়া অনেক উত্তম,0,"Meme, TikTok and others"
এই সব গুলো মুভি আমি দেখেছি,0,"Meme, TikTok and others"
আমরা চাই শাকিব অপু এক হয়ে সংস্যার করুক এবং এক সাথে আবাও ঝুটি বেধে আমাদের কে ভাল ভাল ছবি উপহার দেখএই ঝুটি আমাদের প্রচন্দ,0,"Meme, TikTok and others"
অতিনন্দ্র বাবু একদম সঠিক আমার মনে হয় ওনার সহায়তার অনেক মূল্য,0,"Meme, TikTok and others"
ছলে কে জুত মার,0,"Meme, TikTok and others"
বিশ্বাস করি না সি আই ডি আবার চালু হক,0,"Meme, TikTok and others"
সৌরেরবাচ্চা,0,"Meme, TikTok and others"
শাকিব ভাই আপনি অপু কে মেনে নেয় ভাই আপনি কি বাংলাদেশের ছেলে বলেন ভাই,0,"Meme, TikTok and others"
ওকে ফাঁসি না ওকে গণপিটুনি দিয়া মারা উচিত,0,"Meme, TikTok and others"
পাসি চাই মুদির,0,"Meme, TikTok and others"
রাগে কি করবো কি বলবো ঠিক বুঝতে পারছি না,0,"Meme, TikTok and others"
তা গান দেখে সুধু ভালোলেগেছে,0,"Meme, TikTok and others"
মূওরি খাইছে জিবনেগুনি বেক্তিতুলুনা হিন,0,"Meme, TikTok and others"
সাকিব ভাই অপু আপুএক সাথে ছবি করবেএটাই আমাদের চাওয়া,0,"Meme, TikTok and others"
রানুদি আসলে একজন বেয়াদব তাই তাকে ছুরে দিক আগের মত যেন মানুষের দারে দারে ভিখা করুক,0,"Meme, TikTok and others"
থেকে ছেলেকে ধিক্কার জানাই যেমন তেমন ফল কিছুদিন পর ছেলের ছেলে এভাবেই মারবে,0,"Meme, TikTok and others"
জাকির নায়েক একজন সত্যবাদী তোমার খবর মিথ্যা,0,"Meme, TikTok and others"
ভাই দয়া করে তাকে পিটান ভাই না হয় পুলিশে দেন,0,"Meme, TikTok and others"
সম্পুর্ণ ভিডিও টা দেখার মত সাহস আমার নাই,0,"Meme, TikTok and others"
নৌবাহিনী ভাইয়ারা কেমন করে হাসি সামলিয়ে রাখছে আল্লাহ গো,0,"Meme, TikTok and others"
দুর্ভাগ্যবশত এই লোকটা আমার অফিস কলিগ,0,"Meme, TikTok and others"
এসব বাদ দিয়ে ভালো কিছু কর,0,"Meme, TikTok and others"
ভিউ পাওয়ার জন্যই এই বালের টাইটেল,0,"Meme, TikTok and others"
যারা এটা ভিডিও করছেন তারা কোন বাল ফালাইছেন গিয়ে কেন প্রতিবাদ করলেননা,0,"Meme, TikTok and others"
বেয়াদবটাকে পেটাতে পেটাতে মেরে ফেলা উচিৎ দৃষ্টান্ত মূলক শাস্তির দাবি জানাচ্ছি,0,"Meme, TikTok and others"
তাছরিমা নাছিম সত্যি কথা বেলেছে,0,"Meme, TikTok and others"
কি নামবার,0,"Meme, TikTok and others"
বাঘের বাচ্চা বাঘ,0,"Meme, TikTok and others"
এক দিন সারা বিশ্বে সবাই মুসলিম হবে ইনশাল্লাহ,0,"Meme, TikTok and others"
মিন্নির সোনাই সিমেন্ট দিয়ে ডালাই দেওয়া হোক,0,"Meme, TikTok and others"
ভিখারি রানুর খুব তাড়াতাড়ি পতন হবে,0,"Meme, TikTok and others"
এই বাবার কারণে সে দুনিয়াতে এসেছে আল্লাহ সইবেনা,0,"Meme, TikTok and others"
আমরা মোদির পক্ষে আছি,0,"Meme, TikTok and others"
অনেক ভাল লাগছে সাকিব আর অপুকে আবার বিয়ে কথা সুনে ইতি,0,"Meme, TikTok and others"
ইসলামি আন্দোলন বাংলাদেশ,0,"Meme, TikTok and others"
দুধ আগের চেয়ে অনেক বড় হইছে,0,"Meme, TikTok and others"
সাকিবঅপুআবার দুইজন সিনেমা,0,"Meme, TikTok and others"
তাকে সব পাবলিকের বেন করা দরকার,0,"Meme, TikTok and others"
জুতো মেরে গরু দান হচ্ছে নাকিসব পাগলের প্রলাপ তা ছাড়া কিছুই নয়,0,"Meme, TikTok and others"
চিরদিন সুখে ধাক এটাই কামনা করি অপুও সাকিব কে বলছি,0,"Meme, TikTok and others"
শাকিব খান,0,"Meme, TikTok and others"
ওকে শুলে চড়াও,0,"Meme, TikTok and others"
হে আল্লাহ এ রকরম ছেলে থাকার চেয়ে না থাকা ভাল,0,"Meme, TikTok and others"
কাশ্মীরের চারটি পক্ষ যেমনঃ পাকিস্তান ভারত চিন ও কাশ্মীরের জনগন তাই কাশ্মীর আন্তর্জাতিক বিষয় আন্তর্জাতিক ভাবেই কাশ্মীরের মিমাংসা করা উচিৎ যুদ্ধ সকালের জন্যই খ্তিকর,0,"Meme, TikTok and others"
শাকিব খান তুমি এক থম কথা টা বলছো আমি তোমার অ,0,"Meme, TikTok and others"
বেয়াদব ছিলেন,0,"Meme, TikTok and others"
ভাই দয়া কইরা এই সব ভিডি ও দিবেন না খুব খারাপ লাগে ভাইরে তরে একদিন এই বাবা ছোট থেকে বড় করেছে কত লালন পালন করে বড় করেছে আর তুই তর এই বাবারে কীভাবে মারলি তর তো জাহান্নমেও জায়গা হবে না ভাইরে ভিডিও টার শুরু থেকে অনেকখন কেদেছি কাদতে কাদতে আমি লেখেছি আর তুই,0,"Meme, TikTok and others"
মিদসরকাযাকেরেছেনটিককরছেনটিককরছেন,0,"Meme, TikTok and others"
পুরোটায় নকল মুবি,0,"Meme, TikTok and others"
সাকিব না থাকলে বালো আমি আচি,0,"Meme, TikTok and others"
হাজার সালাম জানাই ওই সাংবাদিক ভাই কে,0,"Meme, TikTok and others"
আল্লাহ আপনি রহম কর প্রিতিবির সকল মা বাফ কে আমাদেরও,0,"Meme, TikTok and others"
মেসি মেসি মেসি আমার প্রিয় খেলোয়াড়,0,"Meme, TikTok and others"
ডাক্তার আপা অন্যের ঝুলা বুনিকে খাড়া করান কিন্তু আপনার বুনিতো ঝুলে রয়েছে,0,"Meme, TikTok and others"
আমিও চাই৷ ওরা এক হোক,0,"Meme, TikTok and others"
মোদী যা করছে ঠিক করছে,0,"Meme, TikTok and others"
এটা মৌসুমির কন্ঠ হতেই পারে না,0,"Meme, TikTok and others"
আল্লাহ যেনো এদের হেদায়েত দেয়,0,"Meme, TikTok and others"
এটা কি মানুষ না পশু আমার মনে হয় পশুও াই কাজ করতে পারবে না,0,"Meme, TikTok and others"
আপনি তো কথাই জানেন না,0,"Meme, TikTok and others"
এরদোগানের মুখে উটের মুত্র দিতে হবে ৷এটা ভারত ৷এরদোগান এমন মার খাবে যে বাপের নাম ভুলে যাবে,0,"Meme, TikTok and others"
ভারতের পতন চাই,0,"Meme, TikTok and others"
এই সব ভিডিও অন লাইনে না দেওয়া ভালো,0,"Meme, TikTok and others"
আজকের ছিনেমা ঃ আব্রাহামের জন্মদিন এ শাবনূর কেন দেরিতে আসলেন,0,"Meme, TikTok and others"
অব্যসই,0,"Meme, TikTok and others"
আৰববে এই নেতা দেশটাকে বেইমানেৰ সমাৰথো কৰছে এটাকে বদশাৰ পদ থেকে বৰখাসতো কাৰা উচিত না হলে খালি দেশ নয় সাৰা দেশেৰ মুছুলমাদেৰ ইজজত সেশ,0,"Meme, TikTok and others"
মানুষ হিসেবে ভালো জাকির নায়েক,0,"Meme, TikTok and others"
আসলে সে নিজেই ভালো মনের মানুষ নয়,0,"Meme, TikTok and others"
টাইটেল কি আর খবর কি সৈদি,0,"Meme, TikTok and others"
আমার খুব ভালো লাগে পূর্ণিমার,0,"Meme, TikTok and others"
ইসলামের মাকে এবং চুদি পাকিস্তানের মাকে চুদি এবং চ্যানেল মাকে চুদি,0,"Meme, TikTok and others"
খাইয়া কাম কাজ নাই তাই আজেবাজে ভিডিও তৈরি করো,0,"Meme, TikTok and others"
কষ্ট হচ্ছেরাগ হচ্ছে সাথে লজ্জা,0,"Meme, TikTok and others"
ৰানু মনডলক তাৰ জীয়েকক দেখা কৰিবলৈ নিদিয়াই ভাল ইমান দিনে খবৰ কৰা নাছিল এতিয়া ভাল দিন দেখা পাই ওচৰলৈ আহিছে,0,"Meme, TikTok and others"
এইবিবাড়িয়া সম্পর্কে বললে ভালো কিছু বলবেন,0,"Meme, TikTok and others"
বাংলাদেশী খবর,0,"Meme, TikTok and others"
আঁখি আলমগীর হলো ভদ্র পতিতা,0,"Meme, TikTok and others"
বাংলা তে ই দিলীপের ফাঁসি চায়,0,"Meme, TikTok and others"
এই গালাগালি করার লোককে নিয়ে আবার আলোচনা,0,"Meme, TikTok and others"
মেয়েদের অপমান খা,0,"Meme, TikTok and others"
রেন্ডিয়ার পক্ষে কেউ হবেনা সবাই কাশ্মীর,0,"Meme, TikTok and others"
পায়ের জুতা পায়ে থাকা ভালো,0,"Meme, TikTok and others"
এটা হচ্ছে পাপের ফল,0,"Meme, TikTok and others"
একজন পতিতার চেয়ে কোন অংশে সে কম নয়,0,"Meme, TikTok and others"
ফালতু প্রোগ্রাম,0,"Meme, TikTok and others"
ও বলেছে এরা সবাই আল্লাহর চাকর কথাটা ঠিক বলেছ,0,"Meme, TikTok and others"
আল্লাহ ওর জায়গা জেনো জাহান্নামে হয়,0,"Meme, TikTok and others"
ওর হাত ভেঙেদেয়ার দরকার,0,"Meme, TikTok and others"
এই হাকিম জালিমের বিচার মুসলিমরা পুত্যাখান করছে জাতি সংগে মামলা দায়ের করা উচিত,0,"Meme, TikTok and others"
মানুস আর মানুস নাই,0,"Meme, TikTok and others"
আমেরিকার প্রেসিডেন্ট কি তোমাদের জামাই,0,"Meme, TikTok and others"
অপুআপুওনেকভাল,0,"Meme, TikTok and others"
না না না না না না না না না না না না না না না না না না না না না না না না না না না না না না না না না না না না না না না না না না না না,0,"Meme, TikTok and others"
বেশি দিন থাকবে,0,"Meme, TikTok and others"
হরেকৃষ্ণ হরেকৃষ্ণ ভারোত,0,"Meme, TikTok and others"
মোদি অমিতশাহার ফাসি চাই,0,"Meme, TikTok and others"
কুলাগার,0,"Meme, TikTok and others"
এটা সুধু হিন্দুদের মধ্যে হয়,0,"Meme, TikTok and others"
আমরা সবায় যা চায় তা হচ্ছে না আমরা সবায় চায় সাকিব অপু এক হক,0,"Meme, TikTok and others"
নিম্ন শ্রেণির অভাবি লোককে কখনো উপরে উঠার শিরি দিতে নেই ওরা যদি একবার কাচা টাকার নেশায় পরে যায় তাহলে ওরা নিজের অস্তিত্বকেই ভুলে যায় থাক পরে যার মাধ্যমে এতো কিছু হয়েছে তার কথা মনে রাখবে আমি নিজেই এব্যাপারে চরমভাবে ভুক্তভোগী কথায় আছেনা অল্প পানির মাছ বেশি পানিতে পরলে যা হয় আর কি,0,"Meme, TikTok and others"
ফালতু চ্যানেল এটা যত মিথ্যা কথা বলে,0,"Meme, TikTok and others"
ওনাকে নেক হায়াত দান করুন,0,"Meme, TikTok and others"
এই বিচার মাত্র আমার মালিক আল্লাহ করবে,0,"Meme, TikTok and others"
তুমার ইমু নাম্বা দেওর,0,"Meme, TikTok and others"
এটা কি মানুষ,0,"Meme, TikTok and others"
আনেক সুন্দর মিলে থাকে তাহলে বিশাল খুশি হবো পৃথিবীর মানুষ গুলো,0,"Meme, TikTok and others"
আরে এর চায়ে কত শিল্পী পরে আছে বুইরা বেডি কি বোজে গানের এমন গান আমরা কত গাই কেউ দেখেনা,0,"Meme, TikTok and others"
জয় শীর রায়,0,"Meme, TikTok and others"
মোদি আর অমিত শাহ এর জন্য জান্নাতের ভিসা নিষেধ এবং মহান রাব্বুল আলামীনের পক্ষ থেকে তাদের ওপর নিষেধাজ্ঞা জারি করা হয়েছে তবে তারা চাইলে জাহান্নামে যেতে পারবে জাহান্নামে ভিসা তাদের জন্য উন্মুক্ত আছে,0,"Meme, TikTok and others"
তোকে তো উল্টো করে পেটানো উচিত তোর বাবার জাওগায় তুই থাকলে বুঝতে পারতি,0,"Meme, TikTok and others"
আপনারা কোন বাল ফালান আমাদের এলাকায় হলে ওরে জুতা দিয়া বাইরাইয়া শিক্ষা দিয়া দিতাম,0,"Meme, TikTok and others"
আইন কে সম্মান করি আশা আইন এর দৃষ্টান্ত মূলক শাস্সি দিবে,0,"Meme, TikTok and others"
আমি চাই তার ফাসি,0,"Meme, TikTok and others"
ধ্যনবাদ,0,"Meme, TikTok and others"
মোসিদ চাই আমিন,0,"Meme, TikTok and others"
তোর মাকে দেখতে জিতের বিপরীতে,0,"Meme, TikTok and others"
সম্প্রতি দেশের এক শীর্ষ গণমাধ্যম জয়া আহসানের নামে ভুল ইনফরমেশন দিয়েছে বলে ফেসবুকে রাগ ঝেড়েছেন এ নায়িকা,0,"Meme, TikTok and others"
ডাক্তার ছেলে না হয়ে যদি মেয়ে হত তাহলে ভালো হত,0,"Meme, TikTok and others"
সুয়ারের বাচছা,0,"Meme, TikTok and others"
ওকে ফাসি দিলেও কম হবে,0,"Meme, TikTok and others"
বাল ছাল ঠাপাই কেউ তোদেরযত সব বাল জীবী হবেই চুপ বাড়া,0,"Meme, TikTok and others"
আলহামদুলিল্লা পারবে দুজন সবার চেয়ে ফাটাফাটি,0,"Meme, TikTok and others"
সালমানের চার বাগের এক ঘাওহবে না এখন কার নায়ক কুথায় সালামান কুথায় এরা কার সাথে কি,0,"Meme, TikTok and others"
জম্মু কাশ্মীর পাকিস্তান পাকসেনা জম্মু কাশ্মীর দখল করো,0,"Meme, TikTok and others"
এডমিনরে প্রশাসনের প্রতি দৃষ্টি রাখার জন্য অহবান করছি,0,"Meme, TikTok and others"
ধিক্কার জানাই এমন সন্তান কে,0,"Meme, TikTok and others"
জঘন্য,0,"Meme, TikTok and others"
হাই সেক্সি আপু আসলে নিতম্ব কি জিনিস আমি তো সেটা বুঝি না আমাকে কি বুঝিয়ে দিবেন,0,"Meme, TikTok and others"
কে কি বল্ল রানু দিদির ব্যাপারে অতিন্দ্র দাদা আপনি মহা মানবের কাজটি করে যান শুভ কামনা রহিল ধন্যবাদ,0,"Meme, TikTok and others"
জিনিস টা একবার যদি চান্স পাইতাম,0,"Meme, TikTok and others"
আসাদ হোলো মাদারচোদ,0,"Meme, TikTok and others"
শাকিব খানকে বাদ দিয়ে দেন ফালতু একটা নায়ক,0,"Meme, TikTok and others"
কোথায়,0,"Meme, TikTok and others"
আপা কেমন আছেন আপনার মোবাইল নাম্বার দাওয়,0,"Meme, TikTok and others"
ছিঃ ছিঃ ছিঃএইসব দিন দেখার জন্যে ছেলেদের বড় করে বাবারা জানোয়ার ছেলে,0,"Meme, TikTok and others"
আমি কিছু বলতে চাই যে সেটা নারী মানুষের জীবন নিয়ে ছিনিমিনি খেলছে,0,"Meme, TikTok and others"
এবলা,0,"Meme, TikTok and others"
শুধু এক হলে চলবেনা এক ছাদের নিচে বসবাস করতে হবে এবং ইসলামের পথে ফিরে আসআমি তোমাদের জন্য সারা জীবন দোয়া করব ইনশাল্লাহআমি কিন্তু সৌদী আরব আছি,0,"Meme, TikTok and others"
অপু বিশ্বাস বাজে মহিলা,0,"Meme, TikTok and others"
সাকিব খান সেরা নায়েক,0,"Meme, TikTok and others"
ছি রানু দি ছি,0,"Meme, TikTok and others"
আপনার সাথে একমত হলাম,0,"Meme, TikTok and others"
লাবলু,0,"Meme, TikTok and others"
পাকিস্তান ন্যায়ের পক্ষে কাজ করছে,0,"Meme, TikTok and others"
এমন পাষন্ড সন্তান থাকার চেয়ে নিঃসন্তান থাকা ভালো,0,"Meme, TikTok and others"
আসলে কি বলবো যখন বুঝতাম না ছোট সময়সিনেমা দেখলে কান্নাকাটি করতামকিন্তু যখন জানলাম বুঝলামসিনেমা জগতটা কত খারাপঐ জগতে মেয়েদের ঢুকতে হয় দেহদিয়ে বিছানায় যেতে হবে ইতারপর যখন সে সেলিব্রিটি বেশ্যা হবেতখন তার সেক্স ভিডিও বের হবে এবং আরও জনপ্রিয় হবে,0,"Meme, TikTok and others"
রানু মণ্ডল কে আবার রানাঘাট নাম্বার প্লাটফর্ম এ ফিরতে হবেই,0,"Meme, TikTok and others"
কে জানে আসল সত্যি টা কি,0,"Meme, TikTok and others"
মোদী পৃথিবীর নিকৃষ্ট শাসক,0,"Meme, TikTok and others"
পায়ের জুতো কখনো মাথায় তুলতে নেই,0,"Meme, TikTok and others"
অস্থির দাদু,0,"Meme, TikTok and others"
এক লিংগো ভাল লাগেনা নিত্য নতুন চায় ভাই তাতে আপনাদের কি সমস্যা নতুন নতুন স্বামী ধরার ও গুন লাগে কয় জন পারে স্বামী বদলাতে,0,"Meme, TikTok and others"
উন্নত মানের ছাগল,0,"Meme, TikTok and others"
পকিস্তান,0,"Meme, TikTok and others"
আপু ঠিক বলেছেন,0,"Meme, TikTok and others"
মেসি তুমি সেরা,0,"Meme, TikTok and others"
ওকে জনসম্মুখে চোখ উপড়ে ফেলে হাত পা কেটে বিচি হাতুড়ি দিয়ে পিষে আগুনে জ্যান্ত পুড়িয়ে ফেলা উচিত,0,"Meme, TikTok and others"
পাকিস্তান ইমরান খান জিন্দাবাদ আমি আছি সারাক্ষণ এর জন্য পাকিস্তানের সাথে,0,"Meme, TikTok and others"
ওকে কুপুয়ে মেরে ফেলা দরকার,0,"Meme, TikTok and others"
আমার এক বার হতে মিনিট এর বেশি লাগে,0,"Meme, TikTok and others"
পুলিশ তার বউকে কেন ধরল না তার বউ কোন প্রতিবাদ করে নাই তার বউকে আগে নেওয়া উচিত ছিল পুলিশে,0,"Meme, TikTok and others"
ভারত জিন্দাবাদ____,0,"Meme, TikTok and others"
মোদি সরকারের উচিত বিচার যেন হয় আন্তর্জাতিক টার্মিনাল,0,"Meme, TikTok and others"
এ ধরনের ভিডিও জন্য ওকিন্তু ধর্ষণ বেড়ে যেতে পারে,0,"Meme, TikTok and others"
এটা কি ঠিক,0,"Meme, TikTok and others"
ময়ুরী যে দিন চলচ্চিত্রে পা রেখেছে সেই দিন থেকে চলচ্চিত্র ধংস হয়ে গেছে,0,"Meme, TikTok and others"
আমার একটা বন্ধু আছে এরকমই বুদ্ধি প্রতিবন্ধী,0,"Meme, TikTok and others"
তবে অপুর সঙ্গে,0,"Meme, TikTok and others"
অপু আপু ঠিক করেনা তবু বলবো অপু আপু কে তালাক দিবেনা অপু আপু খুব ভাল মেয়ে,0,"Meme, TikTok and others"
আপনার কথা গুলি অনেক ভাল লাগলো আপু,0,"Meme, TikTok and others"
তাহসানের ভক্ত এখন আরো বৃদ্ধি পাচ্ছেআর মিথিলার কারণে নারী সমাজে দুর্নাম ছড়াচ্ছে,0,"Meme, TikTok and others"
বাবরীমসজিদ বছরের পুনরো ় জঙ্গি হিন্দুত বাদিরা মসজিদ সালে ভঙাল হল ়আর সুপ্রমকোট রাই দল হাতে আর একর জমি মুসলিম দের দয়াহয় তাহলে বোঝা যাই করে মুসলিম দের সরানো পলেট্রিকস দেশে মুসলমান না থাকলে করাহত না অতএব সামনে মুসলিম দের ভয়াবহ দিন আসছে,0,"Meme, TikTok and others"
এ বাংলাদেশে থাকলে সবাই গনধোলাই দিতো,0,"Meme, TikTok and others"
ভিডিও ফুটেজ দেখে আমার চোখের পানি ধরে রাখতে পারলাম না ওকে রাস্তায় পিষে ফেলা হোক,0,"Meme, TikTok and others"
মোদী জি পক্ষে,0,"Meme, TikTok and others"
সাথে ওর বৌ কেউ শিক্ষা দিতে হবে ওর বৌ দাড়িয়ে দাড়িয়ে দেখছে,0,"Meme, TikTok and others"
বাবার হাইপেসার থাকলে ও বাবা গায়ের হাতকুতা বাচ্চা,0,"Meme, TikTok and others"
স্বামী বিদেশে থাকে বাড়িতে ঢুকানোর মত কেউ নাই যদি কেউ থাক তাহলে আমাকে এ্যাড় দাও,0,"Meme, TikTok and others"
কই কিছু তো বলেন না,0,"Meme, TikTok and others"
শাকিবকে জুতার মালা গলায় দিয়ে সারা শহর ঘুরানো উচিত এতো নামি দামি নায়ক,0,"Meme, TikTok and others"
কারো ছবি ভালো লাগে না সদ্দু সাকিব খানকে ভালো লাগে,0,"Meme, TikTok and others"
তর মাথায় হাড্ডি ভাংমু,0,"Meme, TikTok and others"
জিত সেরা,0,"Meme, TikTok and others"
ইতিহাস পুনরাবৃত্তি হবে,0,"Meme, TikTok and others"
বাবরী মসজিদের রায় সরকারের ইচ্ছায় হয়েছে কোন আইনের তোয়াক্কা না করে অভিযুক্ত বিচারক যৌন কেলেংকারী এই রায় দিতে বাধ্য হয়েছে না হয় বিচারক নিজেই আইনের আওতায় আসতো,0,"Meme, TikTok and others"
আরে মানুষ তো সত্যিই ভগবানের চাকর,0,"Meme, TikTok and others"
অভিনয় তো ভালই জানেন নানু দিদি,0,"Meme, TikTok and others"
এটা কি সত্য কীভাবে সম্ভব,0,"Meme, TikTok and others"
অতিন্দ্রদার ফোন নম্বরটা যদি পেতাম তাহলে একটু কথা বলতাম দাদার সাথে কথা ছিল আমার ব্যাক্তিগত,0,"Meme, TikTok and others"
বিগ করছিলো ঐটাই ঠিক আছে,0,"Meme, TikTok and others"
প্রতিবেশীদের অনেক ধন্যবাদ#অন্যায় হবে যেখানেপ্রতিরোধ হবে সেখানে#,0,"Meme, TikTok and others"
সাকা চৌধুরী রাজাকার থাকলে কিভাবে টানা বার সংসদ সদস্য নির্বাচিত হইছে,0,"Meme, TikTok and others"
সাথে মহিলাটা দারিয়ে দারিয়ে দেখছে এতো খারাপ হাল দেশের ছি ছি,0,"Meme, TikTok and others"
অনেক দিনের ইচ্ছে রেশমি এলনের সাথে কথা বলবি অর বোদা খাইয়া দে চুদনার পুলা,0,"Meme, TikTok and others"
ফাসি ফাসি ফাসি,0,"Meme, TikTok and others"
এই দৃশ্য আমার অতীতকে মনে করে দিয়েছে,0,"Meme, TikTok and others"
ওর পা বেধে পেটানো উচিত,0,"Meme, TikTok and others"
কাশ্মির জয় হবে,0,"Meme, TikTok and others"
আপনি নামাজকে কেনো গালাগালি দিলেন এখন সময় আছে ভালো হয়ে যান আপনাকে হাতের কাছে পাইলে কিজে হতো,0,"Meme, TikTok and others"
মেনে যদি দোষী হয়ে থাকে তাহলে এ পুরুষের কাছ থেকে তিনটি মোবাইল ফোন কোথায় গায়েব হয়ে গেল তাহলে মানুষ কিভাবে পুলিশের উপর আস্থা রাখবে আমি মনে করি মামলাটি সিআইডির কাছে হস্তান্তর করা উচিত,0,"Meme, TikTok and others"
শাস্তি চাই,0,"Meme, TikTok and others"
ওয়া ও দাদু,0,"Meme, TikTok and others"
গুদের ব্যাটা কে ফিঁসি দেওয়া হোক৷,0,"Meme, TikTok and others"
বউ টা রে ও নেওয়া ছিল সাথে,0,"Meme, TikTok and others"
মডার্ন ভিখারি,0,"Meme, TikTok and others"
এটা কি শুধুই মুসলিম জনতার নিউজ চ‍্যনেলমুসলিম হলে ই পাকিস্তান হতে হবেমুসলিম হলেই পাকিস্তানের সমর্থক হতে হবে ভারতের মুসলিম ভাইরা পাকিস্তান পাকিস্তান করবেমাসুদ আজাহার নিষিদ্ধ সণতাসবাদী কী বলল সেটাই খবরের শিরোনামছি ছি এধরনের পক্ষ পাতদুষট চ‍্যনেল বন্ধ করুন আমরা হিন্দু মুসলিম সব ধমের মানুষ নিয়ে এই মহা ভারত,0,"Meme, TikTok and others"
এটা ভারতে মাটিতে চলবে বাংলাদেশে হবেনা,0,"Meme, TikTok and others"
এই সব মানুষের নরকে ও ঠাই হবে না,0,"Meme, TikTok and others"
আমি শাকিবের বকত শাকিবকে→♥ভালোবাসি আমি ★মারুপ,0,"Meme, TikTok and others"
কিছু বলার ভাষা নাইএর বিচার এক আল্লাহ চাডা আর কেও করতে পারবে না,0,"Meme, TikTok and others"
তোমরা মহিলারা অতি সৎ যত দোষ সাধনার কথায় আছে খায় দায় সব্ধু আর মোটা হয় জব্বার হ্যা হ্যা হ্যা,0,"Meme, TikTok and others"
ববুলি কে চাই না,0,"Meme, TikTok and others"
এই রকম ছেলে আর ছেলের বউ যেন আর কোন ঘরে জন্ম না হয় আর এই কুলাঙ্গারকে জনসম্মুখে বিচার করো ভবিষ্যতে এমন আর কেউ না করে,0,"Meme, TikTok and others"
কথার সাথে মুখের মিল নাইএইটা ফেইক,0,"Meme, TikTok and others"
আমার ত এখন বিয়ে করতে ভয় করছে,0,"Meme, TikTok and others"
দেশ বাঁচাও মোদী হাটাও,0,"Meme, TikTok and others"
অনেক ভাল,0,"Meme, TikTok and others"
অাল্লাহর কাছে দোয়া করি ইমরান খানের জন্য অাল্লাহ উনাকে কমতায় রাকেন,0,"Meme, TikTok and others"
যে কোন সুন্দরী রমনীভাবিযে কোন বয়সের মেয়ে আবেদন করতে পারেনআবেদনের শেষ তারিখ আপনার মৃত্যু পরজন্তঠিকানা,0,"Meme, TikTok and others"
দুই খনিকে ঠিক সেই ভাবেই কুপিয়ে মারা উচিত তাদের কেও বুঝিয়ে দেওয়া হক নয়নের মিতুটা কতটা কষ্ট কর ছিলো,0,"Meme, TikTok and others"
মোদীর দুঃসংবাদ শুনতে চাই,0,"Meme, TikTok and others"
নিজেই নিজের শরিলকে টা বাজিয়ে দিলো,0,"Meme, TikTok and others"
এমন কিছু দেখলে নিজের অজান্তেই চোঁখ বেয়ে পানি চলে আসে এদের বিচার চাই,0,"Meme, TikTok and others"
তো তারা এতো খারাপ কাজ করেপরে আবার কি ভাবে লাইভে আশে,0,"Meme, TikTok and others"
তোমার নম্বর দেও,0,"Meme, TikTok and others"
এইটাই দেশদেশের বরতমান অবস্তা,0,"Meme, TikTok and others"
এই ভিডিও টা যে তুলেছে সে ঢুকে এই শয়তান ছেলে টাকে একটা লাথি মারতে পারল না,0,"Meme, TikTok and others"
শয়তীন মিথ্যা খবর,0,"Meme, TikTok and others"
সাকিব কে জূত বাড়ি✌,0,"Meme, TikTok and others"
ভোষ্টা ও নষ্টামি মেয়েদের নিয়ে নতুন কিছু বলার কিছু নেই পিতা ও পুত্র এক সঙ্গে ঐ নষ্টা নারীর সঙ্গে দৈহিক সম্পর্ক গড়ে তুলেছে গোটা মধ্যপাশ্চে জুড়ে বেশ্যা লয়খুলতে চাইছে কেবল মাত্র পশ্চিমাদের খুশি করতে এই বেশ্যা জনকল্যাণমূলক কাজ শুরু করেছে আমেরিকা এই গভীর ষড়যন্ত্র মরহম প্রেসিন্ডে সা দ্দাম হোসেন রহখুব ভালো ভাবে উপলব্ধি করেছিলেনতাই মিথ্যা মারণ অস্ত্রভাণ্ডারে উজুহাতে নির্মম ভাবে হত্যা করা হয়েছিল আজ যুদ্ধবাজ টোনিব্রিলারে কে যুদ্ধবাজ অপরাধ আন্তর্জাতিক ট্রাইব্যুনালে আদালতে ফাঁসি কার্যকর পদক্ষেপ গ্রহণ করা হলো না কেনএটা কোন মুসলিম রাষ্ট্র এমন কিছু করত তাহলে বিশ্ব মোড়লদের আসস্ফলন দেখতে কেমন হতো,0,"Meme, TikTok and others"
কাস্মির ইসুতে আমি পাকিস্তান এর পকহে,0,"Meme, TikTok and others"
এর চরম সাচ্তি দাবি করছি প্রসাশন এর কাছে,0,"Meme, TikTok and others"
শাকিব ভক্তদের সবারই ভালো লাগবে ভিডিওটি একবার হলেও ভিডিওটি দেখুন নয়তো অনেক কিছু মিস করবেন কথা দিলাম ভালো লাগবে,0,"Meme, TikTok and others"
এইসব করেই দেশটারে খাইছেএইটা একটা রোবটএর কোনো অনুভুতি নাইনাসার থেকেও বড় একটা বিজ্ঞান গবেষণার দল আমাদের বাংলাদেশের বালীগযারা এই রোবটের আবিস্কারকদেশের যাই হোকযেকোনও রোগ বালাই হোকতার কোনো অনুভুতি নাইভালো রোবট বলে কথাএখন বাংলাদেশের ডায়েরিয়া হইসেসব বাইর হইয়া যাইতাসেমাগার মারা খুব ভালো আছিএখন অনেকেই আমাকে ভালো ভালো ভাষা বলবে যা কিনা ফেব্রুয়ারিতে আদায় করসিলাম তারাই আবার থাক কি আর কমু🤔🤔🤔 কয়দিন পরে সবাই টের পাইবো,0,"Meme, TikTok and others"
ওর ফাঁসি দিয়ে দাও,0,"Meme, TikTok and others"
তোর স্থান জাহান্নামেও হবে না,0,"Meme, TikTok and others"
দেখবাে,0,"Meme, TikTok and others"
এ মিথ্যা কথা বলে,0,"Meme, TikTok and others"
ঘুষ ছাড়া চাকরি হয় নাকি এখন,0,"Meme, TikTok and others"
আমরা সবাই চাই শাকিব অপু এক হওয়া উচিত,0,"Meme, TikTok and others"
একটা জানোয়ারছি ছি,0,"Meme, TikTok and others"
অনেক অনেক ভালো,0,"Meme, TikTok and others"
আমি এই রায়ের বিপক্খে বিচারপতি গন নেশা গ্রস্ত ছিলো,0,"Meme, TikTok and others"
কাশ্মীরের প‌ক্ষে,0,"Meme, TikTok and others"
এমেযেতেহিন্দু ছিলেন হিন্দু আগে কি মুসলমান ছিলেন নাসবচেয়ে বড্কথাহলেও এখন সাকিব এখন আর অপুকে চাইনাওকে,0,"Meme, TikTok and others"
আপনি নামাজ নিয়ে কথা খারাব কথা বলিয়েন না আললাহু খমা করবে না আপনাকে,0,"Meme, TikTok and others"
আমরা সবাই সাকিব অপুকে চাই,0,"Meme, TikTok and others"
আমরা এই আইনের ঘোর বিরোধিতা করি,0,"Meme, TikTok and others"
নিরবিচারে কাশ্মীরিদের হত্যা কারা সমর্থন করবে,0,"Meme, TikTok and others"
তরুণ প্রজন্মকে অশ্লিল গালিগালাজ শিখাচ্ছে ওই বুইড়া শয়তান,0,"Meme, TikTok and others"
যে ভাবেতোমাকে সবাই কমেনট করছে যদি তোমার লজজা থাকে তবে ভবিশ্যতে এরকম কিছু কোরো না ধন্যবাদ,0,"Meme, TikTok and others"
বাংলাদেশের খবর রাখ,0,"Meme, TikTok and others"
এদের একবার চোখ দুটো বন্ধ হোক তার পর বুঝতে পারবে,0,"Meme, TikTok and others"
এ কি মানুষ একে আমি পাইলে কেটে টুকরা টুকরা করতাম কেউ এনে দে আমার সামনে,0,"Meme, TikTok and others"
গানলেখেতোরমারহেডালেখেনআরকিলেখেনকতটাকাখেয়েচিসমাগি,0,"Meme, TikTok and others"
আর_____এর এক আর গল্প আলাদা,0,"Meme, TikTok and others"
ওর কথায় বুঝাজায় ও রাজাকার,0,"Meme, TikTok and others"
মেয়েটি বড়ই সার্থপর,0,"Meme, TikTok and others"
পাগল মহিলা,0,"Meme, TikTok and others"
আমরা আবারও সাকিব অপু নতুন ছবি দেখতে চাই আর সাবিক তুমি অপু কে বানিয়ে নেও জয়ের জন্য হলেও,0,"Meme, TikTok and others"
তোমার বাডি কোথাই,0,"Meme, TikTok and others"
হ্যালো আপু কেমন আছেন,0,"Meme, TikTok and others"
রানু দি মুরগা বাদ,0,"Meme, TikTok and others"
শুধু ভিডিও করেই ফেসবুকে দেয়নি সাথে প্রতিবাদ করেছে আমদের অনেক কিছু শিখার আছে শাবাশ,0,"Meme, TikTok and others"
এই পুতুলের মুল্য কত কোথায় কিনতে পাওয়া যায়,0,"Meme, TikTok and others"
আমি অনেক মজার ভালোবাসা দিমু যদি কোনো ময়না দের লাগে তাহলে এই নাম্বারে,0,"Meme, TikTok and others"
অপু আপু খুব ভাল মেয়ে বুবলি একটা খানকি বুবলি কে জুতা মারি মাগি তুই তো একটাবাজে মেয়ে,0,"Meme, TikTok and others"
আমি চায় ভারতে সব হিন্দু দেবতা মন্দির স্থাপিত হক,0,"Meme, TikTok and others"
অসভ্য জানোয়ার শালা,0,"Meme, TikTok and others"
এরকম নির্মম ভিডিও দেখলে চোখ দিয়ে এমনি পানি বেরিয়ে আসে,0,"Meme, TikTok and others"
এই আইনের কোন প্রয়োজন নেইদেশে বিভেদের রাজনীতি করছে বিজেপি ও সংঘ যা দেশের পক্ষে খুবই বিপদজনক,0,"Meme, TikTok and others"
অয়তো আল্লাহর আরশ কাপাইছেপ্রতিটা থাপ্পড়ে আল্লাহর আরশ কাপল,0,"Meme, TikTok and others"
আরে ব্যাটা তুই কি মানুষ নাকি অমানুষ তোরই তো বাবা মা এই বাবা কাজ করে খাওয়াইছে বড় করছে এখন এই বাবাকে মারছিস কি করে তোর এই মাইর দেখে আমার বুকে ব্যাথা উঠে গেছে আর কান্না জন্য এস এম এস ও করতে পারছিনা তুই যদি আমার এলাকার হইতি তাহলে আমি তরে পিটাইতাম রে শয়তান,0,"Meme, TikTok and others"
ভুয়া খবর বেটা,0,"Meme, TikTok and others"
ছাগল দিয়ে কে হাল চাষ হয় শাকিবের যোগ্যতা কোনদিন হতে পারবে না,0,"Meme, TikTok and others"
ফালতু নিউজ দেওয়ার জন্য জুতার মালা দিবো তোদেরকে অমানুষের বাচ্চা গুলো জন্মমের দোষ আছে @ নাম শরীফ বাড়ি বি বাড়িয়া সদর থানা,0,"Meme, TikTok and others"
আপনারা নিজে বানান আমরা কিনে নিব,0,"Meme, TikTok and others"
তার সব গুলা কথার লজিক আছে আমি মনে করি তার সব কথা ঠিক আছে,0,"Meme, TikTok and others"
ভাই এই ঘটনা টা কোন জায়গায় ঘটেছে কেউ জানেন,0,"Meme, TikTok and others"
ছবি হিট করার জন্য আপসাদের কত টাকা দিয়েচেন সাকিব অপুকে নিয়ে কথা বল,0,"Meme, TikTok and others"
আই লাভ ইউ জাকির নায়েক,0,"Meme, TikTok and others"
পাকুয়াখালী সন্তু লারমা সন্ত্রাসের ধারা জন কাঠুরিয়া হত্যা,0,"Meme, TikTok and others"
চইতালী ৰায় তুমি খবৰেৰ শিৰোনামি বলো খুব বেছি বালো লাগে বিস্তাৰিত হয়তো পৰে শুনবো,0,"Meme, TikTok and others"
ময়ুরি এখন মমতাজ,0,"Meme, TikTok and others"
অপুর দুধের সাগরে হাবু ডুবু খেতে চাই,0,"Meme, TikTok and others"
উওরা আসব নাম্বার টা দেও প্রিজ,0,"Meme, TikTok and others"
আল্লাহ হাজার হাজার বছর বাচিয়ে রাখুক আমার নূপুর আপুমনিকে,0,"Meme, TikTok and others"
বাবরি মসজিদ রক্ষা করতে পাকিস্তান তুরস্ক হিরান,0,"Meme, TikTok and others"
ওপু মাহি,0,"Meme, TikTok and others"
আমিও চাই দুজন এক হোক,0,"Meme, TikTok and others"
আপনার তদন্তটা সম্পূর্ণ ভুল কোন জেলার মেয়েরা ভালো কোন জেলার মেয়েরা ভালো না এটা আপনার বলতে পারবেন না কেউ যদি ভুল না করে থাকে উত্তরবঙ্গের মানুষ সহজ সরল এটা আমরা সবাই জানি কিন্তু কেউ যদি বিয়ে করে সংসারের যদি অশান্তি না ঢুকে আলহামদুলিল্লাহ সবার সংসারী সুন্দর ভাবে করতে পারে আপনি ফালতু কথা মানুষের সামনে তুলে এগুলি গ্রহণযোগ্য না আপনি কোন জেলার মাইয়া আপনি ভালো না খারাপ আপনি নিজেই জানেন,0,"Meme, TikTok and others"
ভারতের যতগুলো সেনাপ্রধান বদল হয়েছে সবাই চাপাবাজি করে গেছেন এবং এই সেনাবাহিনীও ঠিক একই ভাবে চারচাকা চাপাবাজি করছেন বাস্তবে তারা আজাদ কাশ্মীর এর উপর হাত দেওয়ার তাদের কোনো সাহস নেই,0,"Meme, TikTok and others"
অতিদোন দা তুমি খুব ভালো মনে মানুষ কিতু তুমি এতো অপমান হছেন কেনো জার জন্য এতো বড়ো হলো তেকে অপমান করলো রানু তের মেয়ে,0,"Meme, TikTok and others"
এসব দেখলে সয্য হয়না,0,"Meme, TikTok and others"
ভারতবাংলাদেশের মধ্যে যুদ্ধের কোনো সম্ভাবনাই নেই এসব ভিডিওর কোনো মানে হয় না,0,"Meme, TikTok and others"
মুসলমার আর হিন্দু নাই এই রকমের বিয়াধবি মানতে পারি না,0,"Meme, TikTok and others"
জবাই করে দেয়া দরকার এমন সন্তানকে,0,"Meme, TikTok and others"
এই সন্তানের কঠোর শাস্তি দেয়া হোক প্রয়োজনে মৃত্যুদণ্ড সন্তান নামের কুলাঙ্গার একটা,0,"Meme, TikTok and others"
জামে মসজিদ এর ইমামের বাপের মসজিদ মোনাফেক ঐইমাম,0,"Meme, TikTok and others"
আমরা সবাই সাকিব অপুকে ই পছন্দ করী,0,"Meme, TikTok and others"
এরা হলো সবচাইতে বড় জালিম কারণ বড় জালিম হলো তারা যারা মসজিদ ধ্বংস করে মসজিদে ইবাদাতে বাধাদান করে,0,"Meme, TikTok and others"
অপু অনেক ভালো মেয়ে সাকিব খান কাজটি ভাল করুনা,0,"Meme, TikTok and others"
সানাই কে হার মানিয়ে দিয়েছে ময়ূরীর বডি,0,"Meme, TikTok and others"
ফাঁসি দেওয়ায়া দরকার থাকে,0,"Meme, TikTok and others"
পুলিশদের কাছে অনুরোধ স্টেপ নিন সব জায়গায় এমনটি জেনো না হয়,0,"Meme, TikTok and others"
এগিয়ে জান,0,"Meme, TikTok and others"
মায়েদের কে এমন সাতি হয়া উচিত,0,"Meme, TikTok and others"
নো এনাছি,0,"Meme, TikTok and others"
আমি ও চাই শাকিব খান অপু বিশ্বাস আবারও ফ্লিম করুক,0,"Meme, TikTok and others"
রানুকে আবার আগের জায়গায় ফিরিয়ে দাও রেললাইনে ভিক্ষা করে খাক যারা গান রেকর্ডিং করে তাদের কাছে আমার এটাই অনুরোধ দুদিন শিল্পী না হতেই মানুষকে মানুষ মনে করে না রানু,0,"Meme, TikTok and others"
সাকিব কানের সাতে আমি একমত,0,"Meme, TikTok and others"
আর কিছু দিন পর বাংলাদেশে কেজি হিসাবে শহিদ মিলবে যেমন মিলে বয়লার মূগরি কারন সাকা চৌধুরী নাকি শহীদ এটাই আফছোচআল্লাহ মাফকরূন,0,"Meme, TikTok and others"
তোমাকে এই পৃথিবীর মানুষ আর কি শাস্তি দিবেভাইরে তর জন্য নরক অপেক্ষা করছে তুইও একদিন বাবা হবি শুধু ঈশ্বরের কাছে একটাই প্রার্থনা ছেলেটা যাতে তোমার মতো হয়,0,"Meme, TikTok and others"
তোমাকে আমার বালো লাগল,0,"Meme, TikTok and others"
এক হয়ে যাক,0,"Meme, TikTok and others"
জাকির নায়েক এক ভালো লোগ,0,"Meme, TikTok and others"
কিছু লিখতে পারবোনা ভাইভিডিওটা দেখলাম আর কাঁদলামজীবনে প্রথম এ রকম একটা জানোয়ার দেখার দুরবাজ্ঞ হলো পশু ও অনেক ভালোকারন মাতৃতর দাম দেয়,0,"Meme, TikTok and others"
অখন্ড ভারত দিখন্ডিত মুদি অমিত শাহ,0,"Meme, TikTok and others"
অপু বিশ্বাস কে যারা ভালবাসেন তারা লাইক করুন,0,"Meme, TikTok and others"
আল্লাহ যেনো সব মাবাবার ছেলেমেয়েকে এরকম কাজ থেকে দূরে রাখুক,0,"Meme, TikTok and others"
সময় টিভিকে অসংখ ধন্যবাদ আপনাদের সাথেই আছি আমরাএমন প্রতিবেদনের অনেক অনেক অনেক ধন্যবাদ,0,"Meme, TikTok and others"
হায় দাদু,0,"Meme, TikTok and others"
একটা সন্তান জন্ম দিয়ে বড় করতে যে কত কষ্ট আর ধৈয‍্য লাগে আহারে আভাগা বাবা এমন সন্তান না হলেই ভালো ছিল,0,"Meme, TikTok and others"
দাদার জন্য রানুদি আজ এতবড় গায়িকা হয়েছেন,0,"Meme, TikTok and others"
একটা গরিব মহিলা একটু গান গেয়ে উপরে উঠছে এটা সহ্য হচ্ছে না তোদের এমন নিরীহ একটা রানু দির সমালোচনা করতে গলা কাপে না,0,"Meme, TikTok and others"
আপনে দাই,0,"Meme, TikTok and others"
যাক অবশেষে আমার আত্ত্বায় শান্তি পেলাম উচিৎ শিক্ষা হইছে,0,"Meme, TikTok and others"
ভাত খেতে বসছিলাম কিন্তু ভিডিওটি দেখার পর আর মুঠও খেতে পারলাম না ইচ্ছে করছে ওকে কাচা খেতে পারতাম তাহলে পৃথিবীতে প্রথম সারির একটা ভাল কাজ করতাম,0,"Meme, TikTok and others"
কোন কিছু দেখাতে পারেন নাইতবে এত কথা কেন,0,"Meme, TikTok and others"
ধিক্কার জানাই এইসব সন্তানদের উপর যারা মাবাবার সাথে এমন আচরণ করে আল্লাহ তুমি সবাইকে হেদায়েদ দান করুন,0,"Meme, TikTok and others"
সাহসী নেতা চলে গেছেন দেহ নিয়ে কিন্ত মন থেকে চলে জাননি উনি,0,"Meme, TikTok and others"
আল্লাহর গজব পরবে ওর উপর,0,"Meme, TikTok and others"
আমরা চাই শাকিব খান এবং অপু বিশ্বাস তোমরা আগের মতো এক হয়ে যাও আল্লাহ তোমাদের ভালো করবেন আল্লাহ হাফিজ এক হয়ে যাও,0,"Meme, TikTok and others"
একটা ফাল্তু মেয়ে কিভাবে নায়কা হয়,0,"Meme, TikTok and others"
বেয়াদপ ছেলে,0,"Meme, TikTok and others"
রানুর মেয়েকে আমাদের হাতে তুলে দাও চাকরের আমরা করব বাংলার সব মিলে করব,0,"Meme, TikTok and others"
পথের কুকুর পথে নামানো উচিত,0,"Meme, TikTok and others"
বাংলার একজন সাহসী মানুষ ছিলেন,0,"Meme, TikTok and others"
এই মেয়ে তুমি কেন মিথ্যা বলছ,0,"Meme, TikTok and others"
ফেইসবুকে এমন আর ঘটনা আসে যারা এগুল ভাইরাল করে তাদেরকে বলিএমন কোন ঘটনা দেখেন আপনারা দয়া করে সরাসরি ধরবেন,0,"Meme, TikTok and others"
এই লোকটা এত অসভ্য কেনমরন হয় না কেন এর,0,"Meme, TikTok and others"
এই রায়বিপঙখ,0,"Meme, TikTok and others"
সৌদি মেয়ে বিয়ে করতে চাই,0,"Meme, TikTok and others"
আমি আপনার সাথে একমত শাকিব যেন অপুকে মেনে নেই,0,"Meme, TikTok and others"
আমি আমাদের বস শাকিব খান কে বিসন ভালো বাসি,0,"Meme, TikTok and others"
শাকিব অপু জয় এক হোক,0,"Meme, TikTok and others"
অসাদারন একজন হাসির মানুস,0,"Meme, TikTok and others"
সুইট,0,"Meme, TikTok and others"
ভারত কে খন্ড খন্ড করার এখনই উপযুক্ত সময় ভারত এখন উগ্র হিন্দুদের দখলে,0,"Meme, TikTok and others"
বাংলাদেশ আর পাকিস্তান হাত মিলিয়ে দিক থেকে ইন্ডিয়া কে ধরে ছিবাই শেষ করে দেওয়া উচিত,0,"Meme, TikTok and others"
আপনার মনগড়া তথ্য,0,"Meme, TikTok and others"
সব কিছু সুন্তে পারচি কিন্তু মুহাম্মদ এর নামে খারাপ খতা সুনার পর আর সহ্য করতে পারলাম না,0,"Meme, TikTok and others"
এই ময়ূরী এক সময় সাকিবের নায়িকা ছিল,0,"Meme, TikTok and others"
পাগোল চ্যানেল,0,"Meme, TikTok and others"
মিথ্যা খবর তর ভাই তরে সুদে,0,"Meme, TikTok and others"
আমি রেডি,0,"Meme, TikTok and others"
ঐ মিন্নীর রিমান্ড চাই,0,"Meme, TikTok and others"
মানুষ এত খারাপ হতে পারে আমার জানা ছিল না,0,"Meme, TikTok and others"
এই বেয়াদবের বেচে থাকার কোন নাই,0,"Meme, TikTok and others"
ছিহ,0,"Meme, TikTok and others"
চিত্রজগৎ পাড়ায় কত প্রবিনরা আছে কেউ উদ্দগ নিয়ে অপু শাকিব এর দুই হাত আবার এক করে দিলেই আমরা দর্শকরা খুশি হতাম,0,"Meme, TikTok and others"
আমিতো এনআরসি বিপক্ষে,0,"Meme, TikTok and others"
আপনার ধুদ কি জুলে গেছে,0,"Meme, TikTok and others"
ঢালিউড কিং,0,"Meme, TikTok and others"
ছিঃ ছিঃ রানু মন্ডল ছিঃ কোনো মানোষী কতা নেই আপনার,0,"Meme, TikTok and others"
এই জানোয়ারটা এখনি মেরে ফেলা উচিত কতত নিষ্ঠুর আহারে জানোয়ার কতত গুলো থাপ্পড় দিলো জানোয়ার,0,"Meme, TikTok and others"
আমি সুপ্রিম কোর্টের রায়ের বিপক্ষে,0,"Meme, TikTok and others"
এখন জুতো মেরে গোরু করছেন আল্লাহ বলে একজন আছে এটা কিন্তূ মনে রাখবেন,0,"Meme, TikTok and others"
অপু সাকিব জয়কে চাই আমরা,0,"Meme, TikTok and others"
অপু খারাপ মপয়ে,0,"Meme, TikTok and others"
আমরা চাই সাকিব আপু এক হয়ে সংসার টা করতে কারন আপনারা যদি স্বামী স্ত্রী মিলমিশা না থাকে তাহলে আব্রাহামের ভবিষ্যতে অন্ধকার হয়ে যাবে প্লিজ আপু প্লিজ আপনারা এক হয়ে যাও,0,"Meme, TikTok and others"
দুনিয়াতে এর বিচার না হলে কী হবে আল্লাহ আখিরাতে এর বিচার করবেন,0,"Meme, TikTok and others"
সাইজ কি বাবা,0,"Meme, TikTok and others"
বিগো তোৱ সুনাৱ মদিদে,0,"Meme, TikTok and others"
কুয়েল মললিক নাইকা,0,"Meme, TikTok and others"
এরকম মেয়েদের জন্যই ছেলেদের জীবন নষ্ট হয়ে যায় স্পষ্ট ভাবে @বুঝা গেলো সে একজন দুশচরিএার মেয়ে,0,"Meme, TikTok and others"
আমি এক মত আছি রানু দি ও তার মেয়ে বেইমান,0,"Meme, TikTok and others"
আমারা ‌খমা করে দিয়েছি,0,"Meme, TikTok and others"
আমি চাই বুবলিকে তালাক দিয়ে অপুকে বিয়ে করুক এইটাই আমাদের শেষ কথা তাদের ছেলে হয়েছে তাই তারা মিলেমিশে থাকুক,0,"Meme, TikTok and others"
কাশ্মীর ইস্যুতে পাকিস্তান আর ফিলিস্তিন ইস্যুতে তুরস্ক,0,"Meme, TikTok and others"
তুমি কোন হিরো যে তোমাকে বিআ কোরতে হবেলম্পট একটা,0,"Meme, TikTok and others"
আপনি ভুল ভাবছেন রানু সব বোঝে অতীন্দ্র কথা ছেড়েই দিলাম ভিক্ষারীর কথা বলছে এখন দুদিন আগে তো রানু ভি়ক্ষা করেই খেত আজ সেলিব্রিটি হয়ে ভিখারী বলছে ছিঃ ছিঃ ছিঃ ছিঃ রানু ওর থেকে ভালো গায়ক অনেক আছে আমাদের দেশে,0,"Meme, TikTok and others"
ওর ফাঁসি দেওয়া উচিত,0,"Meme, TikTok and others"
এই বেটিরে মন চায় চুলের মুঠি ধরে উঠাই আর বসাই,0,"Meme, TikTok and others"
যারা এই সমস্ত ভিডিও আপলোড করে তাদেরকে ব্যান করে দেয়া হোক,0,"Meme, TikTok and others"
আঁখি টাকার বিনিময়ে খেলা দেয় ওকে হাজার হাজার মানুষ ব্যবহার করেছে কিন্তু সুখ পায়নি কেউ,0,"Meme, TikTok and others"
ভারত যদি গনতন্ত্রী দেশ হয় তাহলে গনভোট দেয়না কেন,0,"Meme, TikTok and others"
নো কেব নো এন আর চি,0,"Meme, TikTok and others"
লুচ্ছা নাম্বার,0,"Meme, TikTok and others"
সাকিব ভাইাটেকবলেছেন,0,"Meme, TikTok and others"
শাকিব খান সারা বাংলাদেশ গব,0,"Meme, TikTok and others"
মমতাজ আপুআপনাকে খুব সুন্দর লাগতাছে,0,"Meme, TikTok and others"
সাকিবের নায়িকা ছোট দিগী কে চাই,0,"Meme, TikTok and others"
এটা কি পাকিস্তানের দালাল এর চ্যানেল,0,"Meme, TikTok and others"
হুম পাশে আছি,0,"Meme, TikTok and others"
ছি ছি এরকম ছেলে কোনো বাবা মায়ের না হোক,0,"Meme, TikTok and others"
যে ভাই বিডিওটা করছে তাকে অনেন অনেক অনেক ধন্যবাদ,0,"Meme, TikTok and others"
যদি মুদি উজিরে আজম এটা বুঝেন তা হলে কেন তিন তালাক নিয়া নুতন আইন করলেন,0,"Meme, TikTok and others"
সাকিব খান সেরা,0,"Meme, TikTok and others"
সাকিব ভাইয়ের সাথে আমি একমত এবং ঐ অভ্র মহিলা কে উপযুক্ত শাস্তির মাধ্যমে বাঙালী মাবোনদের ইজ্জত ফিরিয়ে দেওয়া হোক,0,"Meme, TikTok and others"
আমরা বাবরি মসজিদ ফেরত চাই চাই চাই,0,"Meme, TikTok and others"
আমি কোন সময় শয়তান দেখিনি তবে আজকে দেখলাম,0,"Meme, TikTok and others"
কুত্তা বাচ্চা,0,"Meme, TikTok and others"
যত্তোসব ফেক নিউজ,0,"Meme, TikTok and others"
আমিও ছাই অপু সাকিব একহয়ে যাক,0,"Meme, TikTok and others"
যেই মেয়ে ধর্ম ছারতে পারে তাকে আর কিবা বলা জায়,0,"Meme, TikTok and others"
মা,0,"Meme, TikTok and others"
বাংলার বাঘআল্লাহ্ ওনাকে জান্নাত দান করুন,0,"Meme, TikTok and others"
ভালো দাদা,0,"Meme, TikTok and others"
মিথিলা সেষ পজন্ত কলঘাট ছাড়া কোন রাস্তা নেই,0,"Meme, TikTok and others"
সাকিল খান সেই লাগে পপি লাগিয়ে দিলেন,0,"Meme, TikTok and others"
আরে ভাই পরিচালকের মন রাখার জন্য নিজের ইজ্জত বিক্রি করে দিবো আমরা কি বলেছি কখনো ছোটো ডেস পরো,0,"Meme, TikTok and others"
আমারত আপনাকে ভালো লাগে,0,"Meme, TikTok and others"
আসল ওপরাধি লাল কিসনো আদবানী,0,"Meme, TikTok and others"
যে অঞ্চলের জনগণ ভারত বিরোধী সে অঞ্চল কি করে ভারত নিজের নিয়ন্ত্রণে নিবে নিতে হলে সব জনগণকে মেরে ফেলতে হবে ভারত কি পারবে সব জনগণকে মেরে ফেলতে যদি মেরে ফেলতে উদ্যেগ গ্রহণ করে তা হলে মহা বিপর্যয় নেমে আসবে ভারতের উপর,0,"Meme, TikTok and others"
এই ছেলে কে জুতা দেই পিটায়,0,"Meme, TikTok and others"
স্বামী স্ত্রী কে ভালবেসে মিষ্টি খাওয়াইছে বলেএই কাজআল্লাহ বিচার করো,0,"Meme, TikTok and others"
সাকিব খানের সাথে আমি একমত এই মেয়ে টা এইটা ফালতু এবং ফাজিল এইটা সববাই জুত মারা,0,"Meme, TikTok and others"
ফালতু জত সব বাংলাদেশ এ বরে গেসে অসব্ব মেয়ে কোথাকার,0,"Meme, TikTok and others"
কুকুরের পেটে ঘি হজম হয় না কখনও ছি়,0,"Meme, TikTok and others"
কোন বাবা জেন এমন না হয় আশিদবাদ করি,0,"Meme, TikTok and others"
আমিও ভগবানের কাছে বলি ওর যেন এরকম সময় আসে তার জীননে,0,"Meme, TikTok and others"
রানুর মতো অনেকেই আছে পোথিবা আলা কিন্তু এ রোকোম অংকারি মানুষ আরনেই,0,"Meme, TikTok and others"
ওরে বছর খাবার না দেওয়া উচিত তাহলে সে বুঝবে,0,"Meme, TikTok and others"
ফকিন্নি আগের যায়গাত যা,0,"Meme, TikTok and others"
আমি হাজার টাকা দিয়ে গরু কিনেছি,0,"Meme, TikTok and others"
হিন্দু মুসলিম ভাই ভাই মোদি সরকারের পতন চায়,0,"Meme, TikTok and others"
বাপ্পিও একটা নায়ক তেলাপোকা ও একটা পাখি,0,"Meme, TikTok and others"
কাশ্মীরের পাশে থাকবো ইনশাআল্লাহ,0,"Meme, TikTok and others"
রানু পাগলি কে খমা করা উচিত নয়,0,"Meme, TikTok and others"
ইস চোখ সইতে পারল না,0,"Meme, TikTok and others"
এই বুড়োটাকে আমি খুব ঘৃণা করি এর যেন খুব শিঘ্রই পতন হয় সেই কামনা করিনাস্তিক বুড়ো কোথাকার‌,0,"Meme, TikTok and others"
রানুদের মেয়ে কোনমতে যাত্রা নদীর কাছে না পৌঁছাতে পারে,0,"Meme, TikTok and others"
গারাপ,0,"Meme, TikTok and others"
কেন শাবানা ভালপ্যাকেট ছবি করেআার আমার কাছে মনে হয় শাবনুর আপুর মত কোন নায়কাই হয় না,0,"Meme, TikTok and others"
পাকিস্তানতোর উপস্থাপনা ভালো লাগে নাশুরু ঠোঁট মিলাশ কা,0,"Meme, TikTok and others"
যে মানুষ তার নিজের ভুল স্বীকার করে তাকে অবশ্যই মাফ করা উচিত,0,"Meme, TikTok and others"
অপু কেবিয়েকরন না,0,"Meme, TikTok and others"
অবশ্যই পারবে দোয়া করি,0,"Meme, TikTok and others"
আমি বুজলামনা কেনো রানু কে নিয়ে এতো বারাবারি হচ্চে নিজের চেহারা আয়না কোনদিন দেখেছে বলে আমার মনে হয় না তাইতো বেবহার এতো জগন্য চি চি চি আর ছালমানকে ও বলি দুনিয়া আর মানুষ পেলোনা যার চেহারা এতো খারাপ যার বেবহার এতো খারাপ তাকে কিভাবে মেনে নেয়া যায় সবাই মনে করলেও আমি মনে করিনা,0,"Meme, TikTok and others"
বিএফডিসি তে এতো কাক কেন শুধু ডাকছে কা কা কা করে,0,"Meme, TikTok and others"
আল্লাহ্ আপনাকে নেককার করুক আমিন,0,"Meme, TikTok and others"
কাশ্মির সাধীন দেখতে চাই,0,"Meme, TikTok and others"
প্রিয়াঙকা চোপড়ার স্বামী নিক জোনাস আমেরিকান শুনতে পেলে কাংলুদের পোদে বাঁশ ঢোকাবে আমেরিকা,0,"Meme, TikTok and others"
নাস ভিডিও,0,"Meme, TikTok and others"
যাদের লজ্জা সরম নাইতাদের মানুষ বলতে লজ্জা হয়,0,"Meme, TikTok and others"
এগুলা কি সত্যি,0,"Meme, TikTok and others"
তোর হাতের সামনে পালে তোর পিটিয়ে মেরে ফেল তাম,0,"Meme, TikTok and others"
হারামী,0,"Meme, TikTok and others"
আমার মতে এরাই বেস্ট জুটি তার থেকেও বড় কথা অপু বিশ্বাস ইসলাম ধর্ম গ্রহন করেছে ওর জন্য আমার অফুরন্ত ভালবাসা আর সম্মান রইল,0,"Meme, TikTok and others"
ফালতু খবর কথা বলতে পারেনা,0,"Meme, TikTok and others"
পাকিস্তান মুসলিম জই হবে হবে,0,"Meme, TikTok and others"
হ্যাঁ আমি ও চাই,0,"Meme, TikTok and others"
ফাসি চাই ফাসি চাই ফাসি চাই ফাসি চাই ফাসি চাই মা বাবার সাথে এমন আবার শুধু মাত্র মিষ্টি খাওয়াবার জন্য ছিঃ ছিঃ ছিঃ ছিঃ ছিঃ ছিঃ ফাসি চাই ফাসি চাই,0,"Meme, TikTok and others"
সাথী রায় যেন রানু দিদির সাথে দেখা না করতে পারে সে ব্যবস্থা করুন,0,"Meme, TikTok and others"
কাশ্মীরের সাধিন চাই,0,"Meme, TikTok and others"
ও একদম ঠিক বলেছে ঢালিউডে ওর প্রতিদ্বন্দ্বিতা করার মতো কেউ নেই কারন ওর মত বোকাচোদা ঢালিউডে আর একটাও নেই,0,"Meme, TikTok and others"
কিছু মানুষ বাবা মায়ের সুখের জন্য নিজে কোরবান হতে রাজি আছে আর এ কুলাংকার তার বাবার গায়ে হাত তুলেছে আমার মনে হয় কেয়ামত খুব কাছে তা না হলে এমন হবে কেন,0,"Meme, TikTok and others"
ওর হাত কেটে দেওয়া উচিত,0,"Meme, TikTok and others"
আপা গাঁজার কি পরিমান খাইলেন হোস পিরলে জানাবেন,0,"Meme, TikTok and others"
ওর যখন ছেলে হবে তখন ঠিক এর থেকেউ আরো অনেক কঠিন ভাবে শাস্তি দেবে ওকে আল্লাহ এর বিচার তুমি দেখিয়ে দিও,0,"Meme, TikTok and others"
না বলে থাকতে পারলাম না তোর ভিক্ষা করাটাই ঠিক ছিল রে বেইমান মেয়ে কোথাকার,0,"Meme, TikTok and others"
রানুর মেয়ে এতোদিনে কোথায় ছিল,0,"Meme, TikTok and others"
তাহসানের উচিৎ ভালো মেয়ে দেখে বিয়ে করা বাজে একটা মেয়েকে নিয়ে না ভাবা,0,"Meme, TikTok and others"
কেরকম খারাপ মানুষ,0,"Meme, TikTok and others"
অনেক দিন পর ময়ূরী কে দেখলাম,0,"Meme, TikTok and others"
সঠিক সিদ্ধান্ত পুরো মুসলিম দেশগুলোকে একাট্টা হতে হবে,0,"Meme, TikTok and others"
এই ভিডিওটা রিপোর্ট করেন সবাই,0,"Meme, TikTok and others"
বাঘের বাছচা,0,"Meme, TikTok and others"
আনলাইক জারা দিছে তারা ওর মতই জারজ সন্তান,0,"Meme, TikTok and others"
এই চেনেল কে করো,0,"Meme, TikTok and others"
বুয়া চ্যানেল সবাই বয়কট করূন,0,"Meme, TikTok and others"
সাকিব আমার প্রিয় নায়ক,0,"Meme, TikTok and others"
ঢত্যূচূঊঊতূএঊঊঊথ,0,"Meme, TikTok and others"
আ হা রে কি কমু খানকির পোলারে একেবারে ফাসি দেয়,0,"Meme, TikTok and others"
গাদা ও নায়ক,0,"Meme, TikTok and others"
অা‌মি খুসি হ‌ভো সা‌কিব খান‌কে ভাদ দি‌লে দার সি‌নেমা অার দেকভনা লুচা লাভার অন,0,"Meme, TikTok and others"
কাশ্মীরেরকে স্বাধীন করা হোক,0,"Meme, TikTok and others"
পাসি চাই পিয়াসার,0,"Meme, TikTok and others"
গ্যাড়ে চরত আছে তো ভারতের সাথে যুদ্ধ কর,0,"Meme, TikTok and others"
বাংলা মুভির সব গুলাই হইছে আবাল কুবাল,0,"Meme, TikTok and others"
ধন্য বাদ ভাই তোমাকে,0,"Meme, TikTok and others"
আপনাদের এই কথা নিয়ে এতো মাতামাতি করার তো কিছু দেখছি না,0,"Meme, TikTok and others"
আমার সামনে পেলে তোকে কচু কাটা করব বেজন্মা,0,"Meme, TikTok and others"
হ্যালো রেশমি আপু আপনি কেমন আছেন,0,"Meme, TikTok and others"
ওঅাইছির এপরিকলপনাজনৃধনৃবাদ সবমুসলিমের উছিতমালাউনের সাথেসমপরকচিনকরা পরজ কেননামালাউনের বোগলে তলেইটা এরাহলোমানবরুপবি পেরাউন,0,"Meme, TikTok and others"
এটা কি করে পারে ভাই আমার জানা নাই,0,"Meme, TikTok and others"
বাবরি মসজিদ ফিরে চাই,0,"Meme, TikTok and others"
ওরে এমন শাস্তি দেওয়া হউক যাতে আর কোন ছেলে মে তার মা বাবার সাথে খারাপ ব্যাবহার না করতে পারে,0,"Meme, TikTok and others"
কাশ্মীরীদের পক্ষ্মে,0,"Meme, TikTok and others"
অমানুষ,0,"Meme, TikTok and others"
বিষশ হাজার টাকার দিব,0,"Meme, TikTok and others"
অবশ্যই পাকিস্তানের পক্ষে,0,"Meme, TikTok and others"
অকে জুতা মার,0,"Meme, TikTok and others"
বাংলাদেশের কিছু হিরোদের কথা বলার স্টাইল দেখলে দুখে হাসি আসে গ্রুমিং করানো উচিত তাদের৷ আমি তাই বাংলা সিনেমা দেখিনা,0,"Meme, TikTok and others"
শামীম ওসমান ভাই কঠিন খেলা হবে🤣,0,"Meme, TikTok and others"
মোদির অমিত শাহ এই দুই সয়তানের বিচার চাই জাতিসংঘের কাছে দাবি ভারতের জনগণের গোটা দুনিয়ার জনগণ,0,"Meme, TikTok and others"
শুভ জন্মদিন জীবন রঙিন হোক,0,"Meme, TikTok and others"
এই মিথ্যা রিপোর্টে মানুষকে বুকা বানিয়ে দিচ্ছেন কেন আপনি হেডলাইনে বলেছেন সৌদি আরব এবং ইরানের সরকারের কথা খবরে দেখলাম অন্য আলোচনা একি সংবাদ আমার বুজে আসেনি,0,"Meme, TikTok and others"
এবংহক এই দুয়া করি চাই,0,"Meme, TikTok and others"
মদিএকার দেশ নয় সব জাতির দেশ একক যখন ছিলনা তখন এ বাতিল করলনা কেন,0,"Meme, TikTok and others"
অবশ্যই অবশ্যই পাকিস্তান তুরুস্ক মালেসিয়া,0,"Meme, TikTok and others"
ডিমবয় হীরু ও সাহসি বীর,0,"Meme, TikTok and others"
কুলাঙ্গার,0,"Meme, TikTok and others"
পরাশক্তি অস্র বেচার ধান্ধায় আছে,0,"Meme, TikTok and others"
আপনি যে পাগল আমরা জানি কিনতু নামাজ নিয়ে গালি দিবেন না,0,"Meme, TikTok and others"
ভারত এখন আর ধর্ম নিরপেক্ষ রাস্ট নয় ভারত এখন আরএসএস জঙ্গিবাদী রাস্ট,0,"Meme, TikTok and others"
কিসের সানাই কিসের টানাই মৌয়ুরির দুধ হলো বিষ সবার চেয়ে বড়,0,"Meme, TikTok and others"
আল্লাহ যে হাত দিয়ে মারলো সে হাত তুমি পঁচায় ফেলো,0,"Meme, TikTok and others"
লোকটি মৃত্যুর আগে যার কাছে বলাতকারের স্বীকার হয়েছিল তাকে বীরের মর্যাদা দেয়া উচিত,0,"Meme, TikTok and others"
খুবি ভালো লাগে,0,"Meme, TikTok and others"
এগুলাও হয় আল্লাহ,0,"Meme, TikTok and others"
অনেক ভালো আলোচনা,0,"Meme, TikTok and others"
অনেক রাজাকারের সন্তান কান্না করতেছে,0,"Meme, TikTok and others"
যে ভিডিও করেছে সে লোক টাকে থামাল না কেন,0,"Meme, TikTok and others"
যে এলাকায় থাকবে ঐ এলাকায় কেউ অপুষ্টিতে ভুগবেনা,0,"Meme, TikTok and others"
এটা আমরা ভাইরাল করেছি,0,"Meme, TikTok and others"
বীর ছবিতে শাকিব বুবলি কে চাই চাই চাই চাই,0,"Meme, TikTok and others"
রানু তুমি এমন ছি ছি,0,"Meme, TikTok and others"
আল্লাহ এইটা কেমন ছেলে,0,"Meme, TikTok and others"
ছিঃছিঃছিঃ মোদী অমিতশাহ,0,"Meme, TikTok and others"
অকে ক্ষমা করা যাবেনা,0,"Meme, TikTok and others"
শাবনুর মহা নায়িকা,0,"Meme, TikTok and others"
তার অনেক বহ্যার খারাপ ছিল তাই জন্য প্রয়োজনীয় হয়ে গেছে,0,"Meme, TikTok and others"
সব মিল,0,"Meme, TikTok and others"
জন্ম দিয়ে কি অন্যায় করে পেলেছে,0,"Meme, TikTok and others"
নাস্তিক ও বেয়াদোব লোকটি,0,"Meme, TikTok and others"
হায়রে সন্তান এই বাবা কত কষ্টো করে নিজে না খেয়ে সন্তানকে খাইয়েছো ধিক্কার জানাই তোর মত অমানুষকে,0,"Meme, TikTok and others"
মুদির ফাসি চায়,0,"Meme, TikTok and others"
ও একটা পতিতা ওর ফাসি চাই,0,"Meme, TikTok and others"
কাঁটা বাচ্চা ভরতে থাকতে পারবিনা,0,"Meme, TikTok and others"
শাকিব আপু আবার এক হক,0,"Meme, TikTok and others"
আমার বাবা দুনিয়াতে থেকে চলে গেছেননা পেরার দেশেআমি বুজি বাবা কি জিনিসবাবা বেচে থাকলে বাবাকে মাথায় করে রাখতামআর সামান্য একটা মিষ্টি জন্য বাবাকে মারলো,0,"Meme, TikTok and others"
তুই এত খারাপ কেন তোর জায়গা কই হবে,0,"Meme, TikTok and others"
ও একটা ইসলাম বিরোধী ওকে শাস্তি দেওয়া হোক,0,"Meme, TikTok and others"
এগুলোর রক্ত দিয়ে গোসল করতে ইচ্ছে করে,0,"Meme, TikTok and others"
সদ গুরু একজন ভন্ডদের হোতা তার লেকচার শুনলে বুঝা যায় তার নিকট আশীর্বাদ নেওয়া পাগলামি ছাড়া কিছুই নয়,0,"Meme, TikTok and others"
এটা কগলাংগার সন্তান,0,"Meme, TikTok and others"
কলা,0,"Meme, TikTok and others"
এক সাতে তাকলে ভালো হবো আমরা চাই,0,"Meme, TikTok and others"
আমার অন্তরিক শুভেচ্ছা ভড়া ভালো বাসা রইল জবা মূখে হাসি থেকে ঠোট গুলি খূব সুন্দর,0,"Meme, TikTok and others"
চিন ও পাকিস্তান মিলে ভারতে ভিতরে ভাগ করে ফেলো,0,"Meme, TikTok and others"
ভাই সালমান শাহর সাথে কাউকে তুলনা না করাটাই ভালো কিন্তু আয়ের দিকে এক নাম্বার দুই নাম্বার ইলিয়াছ কাঞ্চন সালমান শাহকে ধরি কিন্তু সেই সময়ে হল ছিল তেরশহ এখন হল তিনশহ বেদের মেয়ে জোছনা ছবি মুকতি পায়ে প্রায় এগারশহ হলে আয় বিশ কোটি নবাব মুকতি পায়ে একশহ আঠাশটি হলে আয় এগার কোটি আবার নব্বইয়ের দশকে বাংলা ছবি দেখার সুযোগ সুবিধা ছিল বেসি কিন্তু ডিজিটাল যোগে আপনে ঘরে বসেই হলিউড বলিউডের আরো উন্নোত মানের ছবি দেখতে পরতেছেন তাই সে হিসাবে আয়ের দিকে শাকিব খান ও কমনয়ে আমি কি বোজাতে চেয়েছি আপনারা নিশচয় বোজতে পারছেন,0,"Meme, TikTok and others"
আমি তো মুন্নিকে পেলে শাদি করতাম,0,"Meme, TikTok and others"
হেড লাইট এত রড় কেন,0,"Meme, TikTok and others"
ওর এই রকম পোস্ট শেয়ার করা উচিত না আমরাই তার পোস্ট গুলা শেয়ার দিয়ে তাকে ভাইরাল করেছি এতে সে আরো এই রকম ভিডিও করার অনুপ্রেরণা পায়,0,"Meme, TikTok and others"
মুননির ফাসি হবে আগে পরে নয়ন এর,0,"Meme, TikTok and others"
এই মদনা আবার নায়ক কিভাবে হয়,0,"Meme, TikTok and others"
শাকিব খানকে চলচ্চিত্র থেকে বহিষ্কার করা হোক আমরা তাই চাই,0,"Meme, TikTok and others"
কলকাতা জনগণ কে ধন্যবাদ,0,"Meme, TikTok and others"
আমি যেটা দেখছি সেটা সবাই দেখছে তাই নতুন করে বলার কিছু নাইকমেন্ট পড়ে দেখলাম যা ডেলে দেবার তা সবাই দিয়ে দিছে,0,"Meme, TikTok and others"
মুহাম্মদ স এর নামে কিছু বলবি না,0,"Meme, TikTok and others"
কিছু বলতে চেয়েছিলামকিন্তু সবার কমেন্টস পড়ে আর কিছু বলার নাই🤣🤓🤭,0,"Meme, TikTok and others"
আমার সেক্স অনেক বেশি আমার নাম জসিম আমার এক ঘন্টার নিচে মাল আউট হয় না সেই কারণে আমার বউ চলে গেছে আপু আমার সেক্স কমানোর জন্য আমাকে একটা পরামর্শ দেন আমার মোবাইল নাম্বার হচ্ছে,0,"Meme, TikTok and others"
আমি অপুকে খুব ভালবাসিতার কথা হাসি চেহারা আমার খুব ভাল লাগেআর বুবলিকে দেখলে আমার মনে হই টা থাপ্পর মারি,0,"Meme, TikTok and others"
ঠিক হয়েছে আমিও তাই চাই,0,"Meme, TikTok and others"
রাজধানীর বেশির ভাগ প্রেক্ষাগৃহে মুক্তি পেয়েছে শাকিব খান ও শবনম বুবলী অভিনীত রংবাজ অহংকার তৃতীয় অবস্থানে আছে চিত্রনায়িকা পপিপরীমনিডি এ তায়েবের সোনাবন্ধু হাউসফুল রংবাজ অহংকার কিন্তু দর্শকদের সোনাবন্ধু ছবি দেখার তেমন চাহিদা নেই,0,"Meme, TikTok and others"
রানু মণ্ডল গান না গাই অ কিছুই না,0,"Meme, TikTok and others"
ওর কপাল ভালআমার চোখে পরে নাই আমার হাতের ঘুসা ওর পাছা দিয়া যান বের করে দিতাম,0,"Meme, TikTok and others"
ভাইয়া আপনি একটা জিনিস লক্ষ করছেনমিন্নি বার বার নয়ন কে টানা টানি করছেও একবারো রিফাত ভাইয়া একবারো বাঁচানো চেষ্টা করেনি বা ওর সামির পাশে যায় নিঅন্ন্য যারা ছিলো মিন্নি তাদের একজন কে ও ধরেনি শুধু নয়ন ছাড়ামিন্নি নয়য় কে নিয়েই ব্যাস্ত,0,"Meme, TikTok and others"
মাগি,0,"Meme, TikTok and others"
বদমাইশ ছেলে আল্লাহ ওকে সঠিক পথ দেখাক,0,"Meme, TikTok and others"
দিস ইজ খাবিশ,0,"Meme, TikTok and others"
নাউজুবিল্লা ছেলে যেমন বউও তেমন,0,"Meme, TikTok and others"
কসম বলছি তকে আমার সামনে পাইলে একদম উ,0,"Meme, TikTok and others"
আমার সোনার মধ্যে তিল আছে তাতে কি কোন সমস্যা ম্যডাম,0,"Meme, TikTok and others"
গরীবের কথা বাসি হলেও ফলে আপনি যদি আপনার কে বিয়ে করতে চান তাহলে কক্ষনই অতি পরিচিত কে বিয়ে করবেন না বিয়েটা মেয়ে নিয়ে খেলা না তা নাহলে বিয়ে আপনাকে তাহসানের মতই খেলবে,0,"Meme, TikTok and others"
সব মিথ্যা,0,"Meme, TikTok and others"
দারুণ তো,0,"Meme, TikTok and others"
আমাদের দেশে কি মহিলা ডাক্তার উপস্থাপকের অভাব এখানে এক জন মহিলা দিলে ভাল হতো,0,"Meme, TikTok and others"
টিকিআছে নিফুন,0,"Meme, TikTok and others"
শালি খানগি,0,"Meme, TikTok and others"
ঠিকই বলছেন তাদের পরের দিন গুলি বাবা মা ও জয় এক ফ্রেমে বাধাঁ থাকুক আমরা এমনটাই চাই আপনারা ও সজ্ঞে থাকবেন আমরা দোয়া ও করি তাই যেন হয়,0,"Meme, TikTok and others"
আমরা বাবলি মসজিদ বাংটে দেবনা বাবলি মসজিদ জিন্দাবাদ,0,"Meme, TikTok and others"
যত বড়ই অপরাধ করুক বাবার গায়ে এমন ঠান্ডা মাথায় কেউ হাত তোলে অপমানে মরে যেতে ইচ্ছে হচ্ছে,0,"Meme, TikTok and others"
এখনো সময় আছে ভাল হয়ে যান,0,"Meme, TikTok and others"
আপনি কলকাতার কোন চ্যানেল এর সংবাদ পাঠিকা খবরের সাথে মুখের বলার কোনো মিল নেই আর এসব খবর কোথায় পান আপনারা ভারত নিয়ে দেখছি বাংলাদেশের খুব মাথা ব্যাথা,0,"Meme, TikTok and others"
বাবা ত বাবাই তার গায়ে হাত আল্লাহ ওকে মাফ করবে না,0,"Meme, TikTok and others"
সব ফালতু,0,"Meme, TikTok and others"
তাহসান মিথিলার জুটি অনেক ভাল লাগত,0,"Meme, TikTok and others"
আমরা চাই তারা এক হোক আমরা সত্যি সত্যি চাই তারা একসাথে থাকুক,0,"Meme, TikTok and others"
কুলাঙ্গার সন্তান তুই ধ্বংস হয়ে যাবি তোর বাবার বদ দোয়া,0,"Meme, TikTok and others"
অপুর সাথে সাকিব জুটি চাই,0,"Meme, TikTok and others"
ভাই এরকম ভিডিও আরো করেন,0,"Meme, TikTok and others"
ভিডিও ধারণ করা ভাইকে অসংখ্য ধন্যবাদ এবং প্রসাশনকে,0,"Meme, TikTok and others"
আল্লাহ যত দিন মা বাবা বেচে থাকবেততদিন যেন মা বাবা সেবা করতে পারিএটা দেখে চোখে পানি আসলআল্লাহ তুমি তার বিচার কর,0,"Meme, TikTok and others"
ফাঁশানো হচছে,0,"Meme, TikTok and others"
পুরোটাই গুজব টা পুরনো,0,"Meme, TikTok and others"
কথা কিন্তু সত্যে,0,"Meme, TikTok and others"
খুব ভাল আমরা ও চাই দুজনে এক হোক,0,"Meme, TikTok and others"
প্রিয়াংকার ডিভোর্স হয়ে গেছেএখন রাষ্ঠপতি প্রিয়াংকে বিয়ে করতে পারবে,0,"Meme, TikTok and others"
জাগাটা কোথায় আমায় বলুন,0,"Meme, TikTok and others"
মিথ্যা কথা বুঝতে পারছি,0,"Meme, TikTok and others"
আপনার খবর শোনার মতো কিছু নেই তবে আপনাকে দেখে মনে হচ্ছে খুব অল্প দিনেই আপনার ডিভোর্স হয়েছেতাই মাথার ঠিক নেই,0,"Meme, TikTok and others"
ভালো লেগেছে অপু,0,"Meme, TikTok and others"
ওনাকে খুব ই ফালতু আর পাগোল মনে হয়,0,"Meme, TikTok and others"
মূর্খ খালেদার ফাঁসি চাই,0,"Meme, TikTok and others"
মুখের ভাষা ঠিক করুনঃ সন্ত্রাসী কি বলুন স্বাধীনতাকামী,0,"Meme, TikTok and others"
আমিও প্রধান মন্ত্রী কাছে বিচার চাই যে এরকম যাতে কার সাথে না করে কোনো ছেলে মেয়েইডিয়া প্রধান মন্ত্রী কাছে বিচার চাই,0,"Meme, TikTok and others"
জয় শ্রীরাম,0,"Meme, TikTok and others"
বসতির ছেলে জদি হটাত একটা দামি গাড়ি ও একটা পাচতালা বাড়ির মালিক হয় সে কিনতো কি করবে বেবে পাবে না সাকিবের অবসতাও সেরকম হয়েছে,0,"Meme, TikTok and others"
আমি পরতে আইছি,0,"Meme, TikTok and others"
আবার সেই রাস্তার মাঝ খানে ফেলে দিন,0,"Meme, TikTok and others"
বারা বুকটা ফেটে জাচ্ছে,0,"Meme, TikTok and others"
আল্লাহ তোর ওরপ গজব পরুক,0,"Meme, TikTok and others"
জয় হবে পাকিসতানের ইনশা আল্লাহ,0,"Meme, TikTok and others"
আমি সাকিব খান ভাইয়ের সাতে এক মত,0,"Meme, TikTok and others"
আপানার কথা শুনে মনে হচ্ছে আপনার খুব হিংসা হচ্ছে # তাহসানের মোটা ইঞ্চি লম্বা কলম আছে কিন্তু সেটাতে নাই মিথিলার গভীর কুয়া গরমপিচ্ছিল রসে টইটুম্বুর পরিপূর্ণ দরকার শুধু ঘন থকথকে ঝাঁঝালআঠালো এ পরিপূর্ণ শক্তমোটা ইঞ্চিলম্বা কলম বেচারী মিথিলা করবেটা কি প্রকাশ্যে জন কবির ইফতেখার আহমেদ ফহমি তলে তলে নাম জানাঅজানা দিয়েও কোন তৃপ্তি পায় নাই বেচারী মিথিলা সৃজিতই পেরেছে মিথিলার গভীর কুয়ার গরমপিচ্ছিল রসে ইঞ্চিলম্বা কলম সিক্ত করে মিথিলার গভীর কুয়া ঘন থকথকে ঝাঁঝালআঠালো দিয়ে পরিপূর্ণ করে সম্পূর্ণ তৃপ্তি দিতে মিথিলা কি পারে এরকম সৃজিতকে ছেড়ে দিতে মিথিলা,0,"Meme, TikTok and others"
ভাই যে ধরনের কাজ এই ছেলে টা করছে তার বাবার সাতে তাকে ফাসী হওয়া দরকার আমার মতে,0,"Meme, TikTok and others"
এই খবর যারা বিশ্বাস করছে তাদের প্রত্যেকটা বলদ হা হা হা,0,"Meme, TikTok and others"
রাম মন্দির ছিল না মোদির সব চক্রান্ত সরকার এরপর সরকার বলেছি কোনদিন ফয়সালা জানাতে পারেনি মোদী কেন শোনাবে মোদি যেটা করেছি ভুল করেছি মোদী তুমি কোনদিনও সুখে থাকতে পারবে না মরার পরে তোমার বিচার আছে আমার সাথে আমার নাম মোহাম্মদ জসিম,0,"Meme, TikTok and others"
ফরিদপুরের কলংকিত তুরা,0,"Meme, TikTok and others"
প্রতে্্যকটি বিষয়ে শাহারুখ সালমান কে জড়ানো তোমাদের বদ অভ্্যাস হয়ে গেছে আর ভারতীয় বিচার ব্যবস্থাকে যথেষ্ট অপমান করেছে সুপ্রিম কোর্ট এই রায় নিয়ে সারা বিস্বের মানুষ ঠাট্টা করেছে ভারতীয় বিচারকদের এক সম্প্রদায়ের মানুসের বছরের মালিকানা কেড়ে নিয়ে অন্য সম্প্রদায়ের মানুষকে তার মালিকত্ব দিয়েছে শুধুমাত্র িবস্বাসের উপর ভিত্তি করে এটা বিচার নয় এটা অবিচার,0,"Meme, TikTok and others"
এক নাম্বার রাজাকার,0,"Meme, TikTok and others"
আমি মমতা দিদির সাথে আছি কারন ওনায় ভারতের ইতিহাস ভালো যানে,0,"Meme, TikTok and others"
এই সব মিথ্যা কথা বলা বন্ধ করএইকথা হলো য়ে এখানে একদিন মসজিদ হবেয়ে রায়ে রাজনৈতিক মতে,0,"Meme, TikTok and others"
রঞ্জন গৈগের দেওয়া অবৈধ মেরুদণ্ডহীন রায় কোন সহি মুসলমান মেনে নিবে না ইন শা আল্লাহ্,0,"Meme, TikTok and others"
ভাৰতেৰ হিন্দুৰা যদি ভিক্ষা চায় তাহলে আমৰা একড় জমি দেব,0,"Meme, TikTok and others"
অতিনন্দ্রদা আপনি জানেন ভালো কাজে অনেক বাধা আসে আর সবাই জানে আজ রানুদি যেখানে আছে তাও সেটি আপনাদের জন্যে সেটি এ সবাই জানে কোথা থেকে কে এসে রানুদির মেয়ের পরিচয় দিয়ে মেয়েতো প্রমাণ কোরতে পারবে না কারণ বছর আগে তার মেয়ে কোথায় ছিলো তখন তার মা বোলে কেও ছিলোনা এখন যখন সে সেলিব্রিটি মা বোলতে তার কোরছে তাইনা আর নিজে টাকা লুট কোরতে পারছে না বোলে তার মায়ের কাছে থেকে অন্যোকে দোশি কোরছে তাইনা দাদা আমার হিসাবে ওমন মেয়েকে তেজ্যো মেয়ে করা উচিত ওটা মেয়ে না রানুদির বাঁশ ওর কারোনে রানুদির খতি হবে বোলে দিলাম,0,"Meme, TikTok and others"
অনেকেই হয়তো আরো জানতে চাইবে বা করাবে কিন্তু লজ্জায় বলবে না তো এক্ষেত্রে নিজে হতে ঠিকানা দেয়া উচিৎ ছিলো,0,"Meme, TikTok and others"
বিএনপি,0,"Meme, TikTok and others"
এই মসজিদ মুসলমানেদের চলো থাকবে ইংশা আল্লাহ,0,"Meme, TikTok and others"
এই সন্তানের ফাঁসি চাই,0,"Meme, TikTok and others"
বি জে পি হটাও দেশ বাচাও,0,"Meme, TikTok and others"
তুমি অবসর নিলে কাদবে সারা বিশ্ব কে খুশি করবে সারা বিশ্ব মানুষ কে,0,"Meme, TikTok and others"
পশুর মত আচারণ,0,"Meme, TikTok and others"
মাদার চুদ সব মিত্যা নিউজ,0,"Meme, TikTok and others"
এর একটা বিচার চাই,0,"Meme, TikTok and others"
টাকলার মাথা ফাটামু,0,"Meme, TikTok and others"
ভাই নামাজ নিয়ে বা ইসলাম ধর্ম নিয়ে কিছু বলবেন নাধর্ম সম্পর্কে খারাপ কিছু বললে নিজেকে টিক রাকতে পারিনা,0,"Meme, TikTok and others"
আমি ছাই,0,"Meme, TikTok and others"
প্রতিবাদী ভাইদের কে অসংখ্য ধন্যবাদ,0,"Meme, TikTok and others"
ওর আম্মু যখন স্টেশনে পড়ে থাকত তখন কি দেখতে আসত এখন কেন আসলো ওদের মত মেয়েদের ফাঁসি দিয়ে মারা উচিত,0,"Meme, TikTok and others"
বুবলি কে বাদ দেন বুবলি ছবি দেখতে চায় না অপু অপু কে আর শাকিব চায়,0,"Meme, TikTok and others"
অপু তার স্বামীর সাকিবের ছবি মনে হছ্ছে এমন ছবি দিয়ে সংবাদ পরিবেশন করা কতটা শালীন,0,"Meme, TikTok and others"
দেখিস তোকে ধরবে চিনা রুহিঙা বাংলাদেশিদের মারছে কেন জাতি বলে,0,"Meme, TikTok and others"
আহ হা আমার খুব খারাপ লাগলো পাশের মাগিটা কি হুমমম,0,"Meme, TikTok and others"
মেয়েটা নম্বর আসামি,0,"Meme, TikTok and others"
আবোস্তান দেখে,0,"Meme, TikTok and others"
রানু দি মেয়ে তখন কোথায় ছিল যখন রানুদি না খেয়ে টেশনে পড়ে থাকত এখন রানীর টাকা হয়েছে তাই ওর মেয়ে এসেছে,0,"Meme, TikTok and others"
এক সাহাবি রাসুল স প্রশন করল যে হে রাসুল আপনি এই খোলা মাঠে দাড়িয়ে আছেন কেন তখন রাসুল স উওরে বলেন যে হে সাহাবি আমি পূূর্ব দিক থেকে গ্রান পাচছি আর এই কথাটি নবী স পূর্ব দিকে তাকিয়ে বলেছিলেন নবী স আরো বলেন যে পূর্ব দিকে থেকে ধংস হবে তার গ্রান তিনি আরো বলেন যে ভারত বর্ষ আক্রমন এবং মুসলমানদের হাতে ধংস হবে গোটা ভারত আর এই যুদেধর নাম হবে গাজয়াতুল হিনদ এর আরবি অর্থ غزوات الهند,0,"Meme, TikTok and others"
কিং খান মানে ভালো কিছু,0,"Meme, TikTok and others"
অই সব চ্যানেল বন্ধ করা উচিত,0,"Meme, TikTok and others"
শাকিব অপুজুটি চাই চাই,0,"Meme, TikTok and others"
বাগের বাচ্চা,0,"Meme, TikTok and others"
আমি পক্ষে এবং পক্ষে,0,"Meme, TikTok and others"
ওসতাদ সব ঠিক কিন্তু ইসলাম নিয়ে মন্তব্য করবেন না,0,"Meme, TikTok and others"
এর মধ্যে এক কোটি টাকা নামের ছবিটি পরিচালনা করছেন ছটকু আহমেদ মেঘলা নামে ভৌতিক গল্পের অন্য ছবিটি পরিচালনা করছেন ডিপজল কন্যা ওলিজা মনোয়ার,0,"Meme, TikTok and others"
কাস মির,0,"Meme, TikTok and others"
আপনার এই সব বাল চুলের খবর আপনাকে কে এনে দেয় এই সমস্ত নায়িকা ও পরিচালকের শয্যা সঙ্গী ছিলেন নাকি আর বাঙালি হয়ে বাঙলার উচচারণ আপনার এইরকম জঘন্য কেন,0,"Meme, TikTok and others"
এপিজে আবুল কালামএর মতো রাষ্ট্রপতির প্রতিটি কথা যেখানে আমরা অমূল্য বাণী হিসেবে দেখি সেখানে উনার এই কথা গুলো থেকে শেখার কি কিছু আছে জানিনা,0,"Meme, TikTok and others"
নাজিৰু ল আলী,0,"Meme, TikTok and others"
এমেরিকা,0,"Meme, TikTok and others"
জানুয়ার শয়তান,0,"Meme, TikTok and others"
নাম্বার টা দাও,0,"Meme, TikTok and others"
ছাকিবের ভালো কেও চায়না,0,"Meme, TikTok and others"
নাইজ,0,"Meme, TikTok and others"
সংবাদ পাঠকের ঠোট নাড়ানোর সাথে শব্দ চয়নের মিল নেই,0,"Meme, TikTok and others"
আদপাগলির বেটি ফুল পাগলি,0,"Meme, TikTok and others"
বাপ কা রাজ সামাজতাহে সালে,0,"Meme, TikTok and others"
এসব করে কিলাব আচ্ছা তুমি হিন্দু না মুসলিম,0,"Meme, TikTok and others"
কিছু করতে পারবিনা,0,"Meme, TikTok and others"
বেয়াদব,0,"Meme, TikTok and others"
কি করে ভুলে গেলি এই বাপ তোরে জন্ম দিছে আবার ‌বউ এর কাছে বিচার দেয় হারাম জাদারে ইট মারা হোক,0,"Meme, TikTok and others"
চরম বিপর্যয় বাবার গায়ে হাত সহ্য করা গেল না,0,"Meme, TikTok and others"
আমরা গরিবই থেকে যাব যারা ধনি তারা আরো ধনি হবে এই তো দুনিয়া,0,"Meme, TikTok and others"
সিরাজগঞ্জন মিয়েরা ভালো তার কারন কি,0,"Meme, TikTok and others"
শাকিব অপু এক হক ধুবা করি,0,"Meme, TikTok and others"
মুদির গোষ্টি কিলাই,0,"Meme, TikTok and others"
আলোচনার মাধ্যমে সমস্যা সমাধান করা উচিৎ যুদ্ধ করোর জন্যই মংগল বয়ে আনবে না কাশ্মীরে দ্বারা পুনরায় স্হাপন জরুরী,0,"Meme, TikTok and others"
এক দিন ওোরো ছেলে ওকে এই ভাবে মারবে,0,"Meme, TikTok and others"
সানাই এর বড় বোন,0,"Meme, TikTok and others"
শাবাশ এমন সাহসী প্রতিবেশী থাকলে আর কি লাগে,0,"Meme, TikTok and others"
মিন্নি নিরদোস,0,"Meme, TikTok and others"
কি চাও,0,"Meme, TikTok and others"
ওরে ক্রসফায়ার দাও,0,"Meme, TikTok and others"
পাকিসতানজিদাবাদকাশমিরজাকিরনায়েকটিকবলছে,0,"Meme, TikTok and others"
মুদি তুই চা আলা তাই এরকম ভাবনা আসছে,0,"Meme, TikTok and others"
আলহামদুলিল্লাহ শুকরিয়া যে আমি ভারত বাসি তাই বলে অন্নাই কে প্রছয় দেওয়া জাবেনাপাকিস্তান ও কাশ্মীর কে নিয়ে যে সমস্যা তা যেন তাড়াতাড়ি মীমাংসা করেকারণ যে কোন বিষয়ে ভুল ত্রুটি হওয়াটা স্বাভাবিকতাই বলে যুদ্ধ করাটা ঠিক নয় আমি এর বিরুদ্ধে,0,"Meme, TikTok and others"
কাশ্মীর বালুচ ভারোত এর আংশ আছে থাকবে কোনো কেউ বাল ছিরতে পারবেনা,0,"Meme, TikTok and others"
মানুষের রুচি হয় কি দেখে হিজলার চেহারাও তো এর থেকে ভালো 🤣🤣,0,"Meme, TikTok and others"
লেজেন্ডারি লেভেলের মাতৃভক্তি,0,"Meme, TikTok and others"
আল্লাহর নামে শুরু করুন জবাই,0,"Meme, TikTok and others"
আল্লাহ এসব দেখতে চাই না কষ্ট লাগে,0,"Meme, TikTok and others"
যদিও সেফুদা গালাগালি দিচ্ছে তার গুলোর যুক্তি আছে সত্যি দেশে কোন গনতন্ত্র নেই,0,"Meme, TikTok and others"
ইঞ্চি আসে অনেখ তিপ্তি দিমু,0,"Meme, TikTok and others"
মেয়ে টাকে রিমেন্ডে দেওয়া হোক,0,"Meme, TikTok and others"
সাকিব ও অপু জয় হোক,0,"Meme, TikTok and others"
ভারত এতোটাই মৌলোবাদী সাম্প্রদায়িক দেশ যে আল্লাহর ঘর মসজিদ ভাংগার ঘোষণা দিতেও বিবেকে বাধে না যদি কখনো এমন হয় যে মন্দির যতগুলো আছে পুরো দেশে সব ভেংগে ফেলতে হবেকারন আমেরিকা হুকুম দিয়েছে না হলে ভারত দখল করে নিবে এবং সব হিন্দুদের খ্রিষ্টান বানিয়ে গীর্জায় পাঠাবে মনে হয় ভারত রাজী হয়ে সব ভাংগা শুরু করে দিবে,0,"Meme, TikTok and others"
সাকিব ভাই আপনাকে অনুরোদ অপুকে ফালাইবেন না,0,"Meme, TikTok and others"
এক হয়ে যাও আমরা দোয়া করি,0,"Meme, TikTok and others"
জবাই করে দেওয়া উচিত এই হারামজাদাকে,0,"Meme, TikTok and others"
আমাদের প্রিয় ডক্টর জাকির নায়েক উন কে কে ভালবাসেন সবাই লাইক করবেন আল্লাহ ওনার মাথাকে দ্বিতীয় কম্পিউটার বানিয়ে দিয়েছে,0,"Meme, TikTok and others"
আল্লাহ তাআলা যা করেন তা বালের জন্য করেন,0,"Meme, TikTok and others"
মনে হয় সাকিব অপু আর এক সংগে সংসার করবেনা,0,"Meme, TikTok and others"
পাকিস্তান আর্মি,0,"Meme, TikTok and others"
ঠিক বলার জন্য আপনাকে ধনবাদ দিদি,0,"Meme, TikTok and others"
কে কে মহমদ মুদির দালাল তাকে পাথর নিক্ষেপ করে মারা হউক,0,"Meme, TikTok and others"
আমার দেশের চিত্রজগতের একজন তাই আমি ঘৃণা করিনা,0,"Meme, TikTok and others"
ঐ পশুটার কঠোর শাস্তি দেওয়া উচিত,0,"Meme, TikTok and others"
কেউ চাইবেন না মোহিলা খারপ হয়ে যায়,0,"Meme, TikTok and others"
আমি ওচাই মিলে মিসে থাকাৱ,0,"Meme, TikTok and others"
আমরা এই ছেলে বিচার চাই,0,"Meme, TikTok and others"
হিনদু মালাউনদের বেবোহার এই রকোমিই হয়মা বাবার সনমান কি ওরা কি ভাবে বুঝবে,0,"Meme, TikTok and others"
আমি চাচ্ছি যে খানকির পোলারা মাইরালামু দরকার,0,"Meme, TikTok and others"
সাকিব খান একাই একশো তার প্রমান আবার ও দিয়েছে সাকিব খানের পাসওয়ার্ড মুভি বলিউড কে হার মানিয়ে দিয়েছে ইতিহাস গরেছে এই ছবি সত্যি সাকিব খান সেরা হিরো আমরা বস এর সাথে আছি থাকবো সাকিব সেরা হিরো,0,"Meme, TikTok and others"
আমি আগেই ফেসবুকে শেয়ার দিয়ে বলছিলাম বাংলাদেশের শিল্পী দরকার নেই ইন্ডিয়াতে ইন্ডিয়াতে অনেক নামী করা আমাদের শিল্পী রয়েছে কুমার শাওন,0,"Meme, TikTok and others"
নির্দোষ ডক্টর জাকির নায়েক,0,"Meme, TikTok and others"
আফনাছাছকত,0,"Meme, TikTok and others"
বালের খবর ফেক,0,"Meme, TikTok and others"
পতিবন্ধী,0,"Meme, TikTok and others"
এমন শাস্তি দেওয়া উচিত যেন সন্তান বাবাকে বেগ আমার তো পারে পাশে দাঁড়িয়ে থাকা বকু কিছু শায়েস্তা করা উচিত স্বামীর এমন একটা অনুচিত কাজ কি সে বাধা দিল না,0,"Meme, TikTok and others"
তুই নাকি সিজোফ্রেনিয়া রোগী,0,"Meme, TikTok and others"
অভিনন্দন ও শুভকামনা করছি আর্জেন্টিনা,0,"Meme, TikTok and others"
আমাদের বাংলাদেশে এই রকম আমি দেখেছি কিন্তু তখন ছোট বছর বয়সখুভ খারাপ লাগে,0,"Meme, TikTok and others"
ভিতরটা ফেটে গেল এই রকম জানুয়ার ও একদিন বাবা হবে আর তার ছেলে এটাই করবে দুনিয়া বদলের জায়গা যা করবেন তাই পাবেন,0,"Meme, TikTok and others"
অনি ভালো মানুষ,0,"Meme, TikTok and others"
প্রতিটা মার আমার বুকে এসে লাগতেছিল,0,"Meme, TikTok and others"
এ রকম পুলিশ বাংলাদেশে চাই,0,"Meme, TikTok and others"
কিছু বাল পাকনা আছে সাদু সাজে ধুদ বড়ো হেলে বড়ো নলবেনা তো কি ছুট বলবে,0,"Meme, TikTok and others"
কাদবে,0,"Meme, TikTok and others"
এই ভুল সিদ্ধানের ফলে হিন্দু জাতি মুসলমানের কাছে রেড কালার হয়ে থাকল কিছু খারাব হিন্দুর জন্ন ভাল হিন্দুরাও কলংকিত হল,0,"Meme, TikTok and others"
আগে বউ টি মারা উচিতসে চুপ করে ছিল,0,"Meme, TikTok and others"
যাদেরভোটেজিতেছেতাদেরবলেতোমরাভারতেরবৈধনাগরিকতোযেনছেলেমাকেবলছেঐটাআমারবাবাওনারসঙ্গেতোমারবিয়েহয়েছিল তো,0,"Meme, TikTok and others"
এই বিচার পতি কে জন্ম দিয়েছে তার চাচাএটা আমার ওবিশ্বাস ইউর অনার জজঠিক আছে তোমার বিশ্বাস সঠিকএভাবে বলার জন্য দঃখিত ভাষা খুজে পাচ্ছি না বাংলার তেকে ভারতের আদালত ভাল এখন মিলে গেলোআফসুস,0,"Meme, TikTok and others"
আমি করব,0,"Meme, TikTok and others"
আমার মনে হচ্ছে উনি হয়তো না বোঝে এই বাজে কথা গুলা বলছে আসলে বোঝতে পারতেছিনা কি হচ্ছে,0,"Meme, TikTok and others"
মুহাম্মাদ রেপিস্ট,0,"Meme, TikTok and others"
বাংলার মানুষের মুত খা মানুষ হবি,0,"Meme, TikTok and others"
ওনি আমার প্রিয় ব্যক্তি ছিলেন,0,"Meme, TikTok and others"
স্বাধীন হয়ে যদি কাশ্মীর শান্তিতে থাকে তাহলে আমরা সেটাই চাই,0,"Meme, TikTok and others"
মনের অজান্তেই চোখে পানি এসে গেল,0,"Meme, TikTok and others"
নরেন্দ্র মোদী এখন বিশ্ব নেতাদের মধ্যে একজন ব্যক্তি,0,"Meme, TikTok and others"
আমি তোমাদের হাতে দরি রানুর কোন কিছু আপডেট দিবে না আর না হলে ব্লক করে দিব আমি,0,"Meme, TikTok and others"
ওকে মার,0,"Meme, TikTok and others"
তোমাকে চাই,0,"Meme, TikTok and others"
টিক সাকিব,0,"Meme, TikTok and others"
ইকবাল অপুর সংসার ভেঙেছে,0,"Meme, TikTok and others"
জয় কে আমায় দিয়ে দে আমি আর আমার স্বামী জয় কে নিজেদের সন্তানের মতো ভালবেসে বড় করব,0,"Meme, TikTok and others"
আমি ছাই দুজন এক সাতে হক,0,"Meme, TikTok and others"
মোদির গদি চিরস্থায়ী নয় বাবরি মসজিদ পাঁচশত বছরের পুরানো মুসলিমদের সংস্কৃতি,0,"Meme, TikTok and others"
আমরা আসায় আছি কখন আবার শাকিব অপু এক হয়ে শংসার করবে সেটা দেখার জন্য,0,"Meme, TikTok and others"
শুধু লাইক আর কমেন্ট করে হবে না আমাদেরকে আল্লাহর কাছে দোয়া করতে হবে,0,"Meme, TikTok and others"
তোদের ইমান যদি নির্ভেজাল হতো আল্লাহ তায়ালা বাংলাদেশ এর সাতটি খনি এনে দিতেন এবং বাংলাদেশ অভাব মুক্ত হতো,0,"Meme, TikTok and others"
আমারা সবাই দশক হয়ে বলছি অপু বিশ্বাস আরো বরো পরদাই দেখতেই চাই,0,"Meme, TikTok and others"
কলকাতা নিউজ,0,"Meme, TikTok and others"
ডক্টর জাকির নায়েক,0,"Meme, TikTok and others"
নিমকহারাম মোদিকে যে সন্মান দেয় বাটপার মোদি আইন করে মুসলমানদের নিপীড়ন করে তার প্রতিদান দিচ্ছে মরার পর কোন ভোগাস রাম কৃষ্ণ আর শীব এদের রক্ষা করতে পারবে না এক আল্লাহ্ ছাড়া সময় থাকতে এক আল্লাহ্ আর তার রসুলকে মানুন রসুলের কথা মানুন আর মিথ্যা বরজন করুন,0,"Meme, TikTok and others"
মিডিয়া থেকে বের করে দেয়া ইচ্চি ছট লোক বড় হলে এমনি হয়,0,"Meme, TikTok and others"
আল্লাহ রহমত কর,0,"Meme, TikTok and others"
সেই জন্য এতো ভিডিওস,0,"Meme, TikTok and others"
কিয়ামত অতি নিকটে,0,"Meme, TikTok and others"
সাব্বাস বাঘের বাচ্চা আপনি সবার মাঝে বেচে থাকবেনআর বেচে আছেন,0,"Meme, TikTok and others"
এর নিজের কোনো নাই,0,"Meme, TikTok and others"
তার গুলো মনে হয় ত্রকদম সব ছিড়ে গেছে,0,"Meme, TikTok and others"
শাবনূরআমাদেঅনেভেলোলগে,0,"Meme, TikTok and others"
নামাজ নিয়ে গালি দিবেন না,0,"Meme, TikTok and others"
ভারতের এক চুলও ছিড়তে পারবে না,0,"Meme, TikTok and others"
জাকির নায়ক খুবভাল,0,"Meme, TikTok and others"
খেলা হবে আসো খেলবো,0,"Meme, TikTok and others"
আমার কাছে নিয়ে এসো কমিয়ে দেবো,0,"Meme, TikTok and others"
ভালো মানুষ সবসময় অন্যের ভালো চায় কিন্তু যুগটা অনেক পাল্টে গেছে এরপর কারোর ভালো করার আগে অন্তত একটু চিন্তা করে পাবিরিও সুনাম নাহোক দূন্নাম নাহয়,0,"Meme, TikTok and others"
ভাই বেয়াদব বেয়াদবেই থেকেজায় আর মানুষ হয়না আজতাই দেখাইলো ময়ুরি,0,"Meme, TikTok and others"
শালার পুত,0,"Meme, TikTok and others"
আমরা চাই মিলে যাক সাকিব খান এবং অপু বিশ্বাস,0,"Meme, TikTok and others"
মসলিমদের পাসে থাকবো আমি,0,"Meme, TikTok and others"
ধন্যবাদ সময় টিভি ও ভিডিও যে করছে তাকে,0,"Meme, TikTok and others"
শিক্ষিত নামের কলংক,0,"Meme, TikTok and others"
এর ঘর কথায় যে বলবে,0,"Meme, TikTok and others"
তুমি দেখতে আমি আপনার সঙ্গে কথা বলতে চাই,0,"Meme, TikTok and others"
ইমরানখান কেছালাম,0,"Meme, TikTok and others"
সবকয়টাই তো মূর্খ,0,"Meme, TikTok and others"
হায়রে সন্তান যার জন্য তুই পৃথিবী দেখলি তার গায়ে হাত তুলেছে এমন কুলাঙ্গার সন্তান বেঁচে থেকে লাভ কি,0,"Meme, TikTok and others"
কোন কি মিরাকল ঘটতে পারে না যাতে তারা আবার এক হয়ে যায়,0,"Meme, TikTok and others"
ওকে গনো পিটানি দিয়ে মেরে ফেলা হোক এলাকা বাসি,0,"Meme, TikTok and others"
চুলকানি হলে যা হয়,0,"Meme, TikTok and others"
রানো কে বার করে দাও সালি ভিকারি,0,"Meme, TikTok and others"
পাকিস্তান জিন্দাবাদ কশ্মীর জিন্দাবাদ জিন্দাবাদ ইসলামের জিন্দাবাদ মহা নবি সাঃ ইসলামের হবে জয়,0,"Meme, TikTok and others"
ছেলের বউটাকেঊ নিয়া উচিত ছিলোকারন মহিলা টা পাশে দাডিয়ে কোন বাঁধা দিল না সি থুতু তোদের মুখে তোরা অমানুষ যে ভিডিও করেছে তাকে ধন্যবাদ,0,"Meme, TikTok and others"
ফেরদোস স্মার্ট ও শিক্ষিত,0,"Meme, TikTok and others"
আমরা চাই সাকিব ভাই আপুকে আবার ও বিয়ে করুক,0,"Meme, TikTok and others"
ওর হাত দুটো কেটে ফেলা উচিৎ কে কে একমত আছ,0,"Meme, TikTok and others"
ভারত তে বিয় পকে,0,"Meme, TikTok and others"
দেশেকোনআইনেশাশননাইবলেএইরকমচলেসবহাসিনারজনৃএমনহচচে,0,"Meme, TikTok and others"
অনেক ভাল লাগল,0,"Meme, TikTok and others"
আর একটা কথা রাখে আল্লা মারে কে,0,"Meme, TikTok and others"
তওবা কর সেফাত,0,"Meme, TikTok and others"
বাবরি মসজিদ চাই এখানে,0,"Meme, TikTok and others"
আমাদের দেশের সংসদে গালি হয় সেই দেশ কতটা অসভ্য হতে পারে,0,"Meme, TikTok and others"
শাকিব বুবলি জন্য বাদ হয়েছে,0,"Meme, TikTok and others"
এই পশুকে উপযুক্ত শাস্তি দেওয়া হোক,0,"Meme, TikTok and others"
সালমানের বাবা কাফের,0,"Meme, TikTok and others"
ওদের বিয়ের কোন ঠিক নাই,0,"Meme, TikTok and others"
কিছু মানুষ দেখি ঝুলেপড়া বড় বড় দুধ দেখে পাগল হয়ে গেছে আরে একবার ভাবুন ব্রা ও জামা পড়ার পরও কেমন ঝুলে আছে খালি গায়ে কতটা বিশ্রী লাগবে কোথায় দুধের মাথাটা গিয়ে পড়বে,0,"Meme, TikTok and others"
আমার একটি পাত্র লাগবে,0,"Meme, TikTok and others"
সাকিব খান কিভাবে থাকে ছেলে কে ছারা এটা একটা অবাক বিষয়,0,"Meme, TikTok and others"
শুভ জন্মদিন প্রিয় সুপারস্টার এগিয়ে যাও শুভ কামনা রইলো,0,"Meme, TikTok and others"
ওকে ক্রস ফায়ার দেওয়া হোক,0,"Meme, TikTok and others"
আমি বাংলাদশী হয়েও বলছি অতিন্দ্রর মত ভালো মানুষ পৃথীবিতে খুব কম পাওয়া যাবে খুব ভালো মানুষ সে শাস্তি দিতে হয় তার মেয়েকে দেওয়া হোক,0,"Meme, TikTok and others"
ধর্ম নিয়া কথা কস আল্লাহ ক্ষমা করবে না তোরে,0,"Meme, TikTok and others"
তুমি জান ধনএকজন পর্নস্টার কমকরে একটা পর্ন মুভি হতে একলাখ ডলার আয় করে,0,"Meme, TikTok and others"
শয়তানের খাড়া ঝিলকি,0,"Meme, TikTok and others"
আমার হাতে য়দি এমন কোন আইন থাকতো আমি ওরে মেরে ফেলতাম,0,"Meme, TikTok and others"
মোরা এক বৃন্তে দুটি কুসুম হিন্দু মুসলমান,0,"Meme, TikTok and others"
আমিচাই কাশমির পাকিস্থান থাকুক,0,"Meme, TikTok and others"
জাকিরনায়োককারোজন্যহুমকিনাজাকিরনাওকসবাইরকেসটিকপতবাতাইতেচেনআলোরপতেআসারআহাব্বানাজাইতেচেন,0,"Meme, TikTok and others"
কপাল আমাগো বাংলাদেশি কেন হয় না এমন,0,"Meme, TikTok and others"
অতীন্দ্র যদি সেদিন স্টেশন দিয়ে না যেত তাহলে রাণু দি আজ স্টেশন এই বসে থাকতো,0,"Meme, TikTok and others"
আল্লাহ তোকে যা দিয়েছিলো তাই সুন্দর ছিলো এখন তোকে দুধ দেয় গরুুর মতো দেখায়,0,"Meme, TikTok and others"
এরা কেমন মানুষ যে আল্লাহ ঘর ভাঙতে চায় আল্লাহ তাদের উপর রহমত দান করেন,0,"Meme, TikTok and others"
চাচি এই খবর কার থিকা পাইছেন কোন ফেরেশতা দিছে,0,"Meme, TikTok and others"
ম তোর কপালে জুতার বারি সিফাত উল্লাহ নাম লইলে,0,"Meme, TikTok and others"
রানিদির ফ্যানরা লাইক করুন,0,"Meme, TikTok and others"
এই চেনেলটা বন্ধ করে দেওয়া হোক যারা রাজি আছেন তারা লাইক দিন,0,"Meme, TikTok and others"
যত বড়ই সেলিব্রিটি হয়ে থাক উনার কিন্তু স্বভাবটা খুবই খারাপ জাহির করুক কিন্তু আমাদের ধর্মকে নিয়ে টানাটানি করে ওর ফাঁসি চাই আর কোন কথাই শুনতে চাই না,0,"Meme, TikTok and others"
এক দম বাকোয়চ ভিডিও টিএবং সব কথা গুলোই মিথ্যা,0,"Meme, TikTok and others"
সবকিছুর পিছনে অর বউয়ের অবদান চির সরনীয়,0,"Meme, TikTok and others"
উসটা মরি তর হতার ভিতরে,0,"Meme, TikTok and others"
লাউ মাসাল্লাহ,0,"Meme, TikTok and others"
লুচ্চা,0,"Meme, TikTok and others"
কান্না থামাতে পারেনি জালেম ছেলে,0,"Meme, TikTok and others"
এটা মিথ্যা কথা,0,"Meme, TikTok and others"
আগে হোক তারপর,0,"Meme, TikTok and others"
হিন্দুত্ববাদি উগ্রবাদীদের অকাট্য বিশ্বাস জেগে উঠেছে বছর হতে যেখানে মুসলমানদের উপাসনা চলে আসতেছিল,0,"Meme, TikTok and others"
টাক কাকু নামাজ নিয়ে গালি দেওয়া টা আপনার ঠিক হয়নি আর সব ঠিক আছে,0,"Meme, TikTok and others"
ও এই কালের কাফের কাফের উপর দিয়া কফের কি জানি হবে ওর কাফেরের,0,"Meme, TikTok and others"
বুঝলামনা প্রতিবেশী গুলা কিছু করছেনা কেন,0,"Meme, TikTok and others"
আমার ভালো লাগতো,0,"Meme, TikTok and others"
মুনাফিক ছাড়া সবাই পাকিস্তান কাশ্মীরের থাকবে,0,"Meme, TikTok and others"
ভাইয়া ভিডিওটা দেখে চোখের পানি ধরে রাখতে পারলাম না ওকে পাবলিক গণ পিটানুতে মারা উচিত,0,"Meme, TikTok and others"
কথা গুলো সত্যি,0,"Meme, TikTok and others"
বলুন তো সাদা শার্ট পরা লোকটি দারিয়ালা লোকটির কানে কি বললো,0,"Meme, TikTok and others"
এরকম কুসন্তান কারো যেন না হয়,0,"Meme, TikTok and others"
দুনিয়া ছলে য়াবে এমন সময় হয়ছে ইমান ছলে গেছে সবার,0,"Meme, TikTok and others"
ও একটা জারুজ,0,"Meme, TikTok and others"
যে এই ভিডিও করে পাপিকে ধরিয়ে দিয়েছে তাকে অনেক ধন্যবাদ,0,"Meme, TikTok and others"
পাকিস্তানের রুটি খাওয়ার পয়সা নেই ৷ ভারতের সাথে যুদ্ধ পাকিস্তান যুদ্ধে জড়ালে বেলুচিস্তান স্বাধীনতা ঘোষণা দিবে ৷ টুকরো টুকরো হবে পাকিস্তান ৷ মোদী সরকার কাশ্মীরকে সুপথ দেখালেন ৷ মোদীকে অভিনন্দন ৷ কাশ্মীর স্বাধীন হলে পাকিস্তানের মত উগ্র মুসলিম সন্ত্রাসী দেশ হতো ৷,0,"Meme, TikTok and others"
মেয়েটিকে ধোরে রিমান্ডে কেনো নেয় না এখনো,0,"Meme, TikTok and others"
যেমন দেশ তেমন মানুষ তেমন ভাবনা,0,"Meme, TikTok and others"
রানু দি এবার শেষ,0,"Meme, TikTok and others"
যিনি বলছেন তার নিজেরটা কি ঠিক আছে,0,"Meme, TikTok and others"
সমগ্র নাস্তিকের দল,0,"Meme, TikTok and others"
তাহলে বাংলাদেশে যত হিন্দু আছে সব ভারত পাঠিয়ে দেয়া হোক আমৃত শাহ রেখেদেবে,0,"Meme, TikTok and others"
সুন্দরী মেয়েদের ফটো চাই,0,"Meme, TikTok and others"
ওদেরকে প্রমাণসহ চিহ্নিত করে সরকার যদি ক্রস ফায়ার এর অর্ডার করতো তাহলে খুব ভালো হতোএই আইনটা সমাজ ও দেশের জন্য বৃদ্ধ মাবাবার জন্য খুব দরকার তাহলে আর এগুলো মাবাপের উপর কেউ অত্যাচার করতে সাহস পেল না,0,"Meme, TikTok and others"
তোমাকে আবারো ভিখারি বানাতে আমাদের কিন্তু বেশী সময় লাগবে না তাই যে টুকু ভালোবাসা পেয়েছ সেই টা হারিয়ে যেতে দিও না,0,"Meme, TikTok and others"
এটাকে জুতা ঝাড়ু দিয়ে পিটিয়ে দিন,0,"Meme, TikTok and others"
জেমোন কর্ম তেমন ফল,0,"Meme, TikTok and others"
আমি ভারতীয় তাই ভারতের পখ্খে,0,"Meme, TikTok and others"
ছাগলের ও মুখ ঢেকে রাখছে,0,"Meme, TikTok and others"
খুব অন্যায় করছেন মহাপাপি ওর শাস্তি দরকার,0,"Meme, TikTok and others"
নাইস ভিডিও,0,"Meme, TikTok and others"
আমার দাবি বাবড়ি মজিদ চাই এই রাই আমি মানি না মানি না,0,"Meme, TikTok and others"
পাকিস্তান যুদ্ধ শুরু করলে পাকিস্তানকে ধুলির সাথ করে দিতেহবে,0,"Meme, TikTok and others"
বিয়াদপ,0,"Meme, TikTok and others"
আল্লাহর ঘর আল্লাহ নিজে রহ্মা করবেন তোমরা শয়তান যারা বাড়াবাড়ি করছো নিশ্চয় জালিমদের স্থান জাহান্নামে,0,"Meme, TikTok and others"
এই মেয়েকে দিয়ে নাটক সিনেমা গান বিজ্ঞাপণ কোন কিছু বানাবেন না,0,"Meme, TikTok and others"
হায়রে ভগবান এ কেমন ছেলে,0,"Meme, TikTok and others"
মিথ্যে বলেইতো মনে হলো,0,"Meme, TikTok and others"
কেন আমি জানাবো জে আমি বি ন পি না আওয়ামিলিগএসব ফাযলামি বাদ দেন,0,"Meme, TikTok and others"
সময় টিভিকে ধন্যবাদ এইটা প্রচার কারার জন্য ওকে কঠিন আকারে শাস্তি চাই,0,"Meme, TikTok and others"
হ্যালো ম্যাডাম ভারতের ধ্বংস চায় বাংলাদেশ বিএফ বিপক্ষে গেলে ভারতের পাকিস্তান বোম্বে বাংলাদেশ এশিয়া,0,"Meme, TikTok and others"
ওকে দেখ তে চাই না বাংলাদেশ পুলিশ হিসাবে,0,"Meme, TikTok and others"
কোথায় আজ ভালোবাসা আর সম্মান কি স্বাস্তির বিধান এর জন্য,0,"Meme, TikTok and others"
প্রিয় ব্যাক্তি আব্দুল হামিদ স্যার,0,"Meme, TikTok and others"
ওরফাসিচাইওরফাসিচাইওরফাসিচাইওরফাসিচাইওরফাসিচাই,0,"Meme, TikTok and others"
আমরা সবায় খুশি সাকিব কে চবি থেকে বাদ দেয়া হক সাকিব লুচচ সালা নাববর বেহাদব সাকিবের চবি আর কন দিন দেখতে জাবনা নানানা আর না,0,"Meme, TikTok and others"
হ্যালো তুমি চিনেন মুসলমানদেরকে হেফাজত করো আল্লাহ সাহায্য,0,"Meme, TikTok and others"
মহামান্য রাষ্টপতি অাপনি মন খুলে কথা বলেন এজন্য ধন্যবাদ তার সাথে যদি দেশে মোসলমানের দেশে ইসলামি শাসন ব্যবস্হা জন্য উদ্যোগ নিতেন সবচেয়ে ভাল হতো,0,"Meme, TikTok and others"
জানয়ারা,0,"Meme, TikTok and others"
এর মতো হতাভাগা আর আছে কত্তবড় খারাপ,0,"Meme, TikTok and others"
ছি ছি দিনে দিনে আরো কত কি দেখতে হবে হায় আল্লাহ তুমি সকলে সুবুদ্ধি দাও,0,"Meme, TikTok and others"
সেক্সি মেয়েরা ফোন দিবা চুদে মজা দিব,0,"Meme, TikTok and others"
একজন সাংবাদিক কখনো এভাবে উপস্থাপনা করতে পারে না লীগের দালাল তরা,0,"Meme, TikTok and others"
চোখে পানি চলে আসছে,0,"Meme, TikTok and others"
যদি কোন মেয়েরা ইমু সেক্স করতে চাও ফোন দাও ইমু নাম্বার,0,"Meme, TikTok and others"
রানুদিকে কে কে মাফ করে দিয়েছেন,0,"Meme, TikTok and others"
যেই হাত দিয়ে মারছে সেই হাতটা পুড়ে ফেলা উচিত,0,"Meme, TikTok and others"
ম্যাডার আপনার সাইজ কত,0,"Meme, TikTok and others"
আওমীলীগ থেকে অনেক ভাল,0,"Meme, TikTok and others"
প্রতিটি থাপ্পড় যেন আমার কলিজায় মারল ওকে ফাসি দেয়া হোক,0,"Meme, TikTok and others"
আয়রা তুমি ভালো থেক,0,"Meme, TikTok and others"
শাকিব বাই বাংলাদেশের দুই বাংলা কিক খান,0,"Meme, TikTok and others"
কারো পক্ষ মিথ্যা স্বাধিকার হারিয়ে স্বাধীনতার পথে কাশ্মীরকে অনেক মুল্য দিতে হবে দুর্বলের পক্ষে ট্রামবাজরা তো না থাকারই কথা,0,"Meme, TikTok and others"
আলহামদুলিল্লাহ ইরান,0,"Meme, TikTok and others"
সব চেয়ে ছোট ব্রা সাইজ হলো সানাইয়ের অনেক ছোট,0,"Meme, TikTok and others"
এনারসি চায় না,0,"Meme, TikTok and others"
এক হওয়াটা বিশাল ব্যাপারঅপু কে অন্য আরেক জনের সাথে বিয়ে বসতে হবে তারপর যদি সে তালাক দেয় তাহলে শাকিব বিয়ে করতে পারে,0,"Meme, TikTok and others"
তোমোরা এতো বেইমান কেন তোমাদের স্বাধিনতা তো আমরাই দিয়েছিলাম,0,"Meme, TikTok and others"
ভাই তর গাড়ি ভাড়া আমি দিবো তুই আমার কাছে আয় তরে মাইরা আমি ঘুম আসমু,0,"Meme, TikTok and others"
যিনি খবর বলছেন উনার ঠোঁটে কিন্তু কথার সাথে ম্যাচ করছে না সব ফেক নিউজ জুতোর বাড়ি কেলাতে হবে,0,"Meme, TikTok and others"
টা যেভাবে লাগালেন মনে হচ্ছে আপনি ওদের মধ্যেকার একজন,0,"Meme, TikTok and others"
রেশমি তোমার সাথে আমি কথা বলতে চাই কি ভাবে তোমার সাথে কথা বলবো প্লিজ আমাকে একটা লিংক দাও না হলে আমাকে তোমার নাম্বার টা দাও প্লিজ তোমার সাথে কথা বলার খুব ইচ্ছা,0,"Meme, TikTok and others"
এইটা কি কোন ছেলের কাজ আমার বাপ যদি আমাকে কেটে কুচি কুচি করেও ফেলে তারপরে আমার বাবার চোখের দিকে তাকানোর সাহস নেই আল্লাহ কিছু বলার ভাষা নেই,0,"Meme, TikTok and others"
আপনার নিজের স্তনই ঝুলে গেছে আগে নিজেরটা ঠিক করুন পরে পরামর্শ দিন,0,"Meme, TikTok and others"
আবার ফিরে অপু বিশ্বাস শাকিব খান এই জুটি আমি চাই,0,"Meme, TikTok and others"
মানবাধিকারের পক্ষে,0,"Meme, TikTok and others"
আমিও চাই শাকিব ওঅপু এক হয়ে যাক,0,"Meme, TikTok and others"
শাকিব খান নিজেই ত লুচ্জা,0,"Meme, TikTok and others"
আমরা সবাই একহযে থাকতে চাই হিন্দি মুসলিম বাই বাই জারা দেশকে বাটতে চায তাঁদেরকে হটাও দেশ বাঁচাও,0,"Meme, TikTok and others"
আবার ওনার হাতে বাটি চলে আসবে,0,"Meme, TikTok and others"
রানুর কন্ঠ ভালো কিন্তু মনুষ্যত্ব বলে কিছু নেই আর থাকবে কি করে মনুষ্যত্বের জন্য লেখা পড়ার দরকার হয় ওনার তো আর সেটা নেই,0,"Meme, TikTok and others"
তোর দুই হাত দংস হক আল্লাহ এ অপমানের বিছার করবেনসবার আগে চেলের বোয়ের বিছার করা হক,0,"Meme, TikTok and others"
ওর হাত কাটা হোক,0,"Meme, TikTok and others"
বাংলাদেশের উচিত পাকিস্তানে যোগ দেবার জন্য আন্দলোন করা,0,"Meme, TikTok and others"
বাংলাদেশে এমন হলে খুব ভালো হতো,0,"Meme, TikTok and others"
একফুট জায়গা প্রতিবেশী কে যাঁরা ছাড়ে না তাঁরা সব ছেড়ে দিবে এই স্বপ্ন যাঁরা দেখছে তাদের জেনেরাখা দরকার আগুন কোনো জাত দেখে না এই দেশে কেবল থাকবে অন্যদেশের সংখ্যালঘু রা বর্তমানে যাঁরা ভারতে বাসকড়ছে তাঁরা ধর্মযুদ্ধের আগুনে শেষ হয়ে যাবে অমিত শাহ এর বুদ্ধি গরুর মতো সেটা আজ বুঝতে না পারলেও আগুন জ্বললে সবই বুঝবে,0,"Meme, TikTok and others"
পূজা চেরি কি আমার ভালো লাগে,0,"Meme, TikTok and others"
কি ক্যাপশন আর কি নিউজ যতসব ফালতু রিপোর্টার,0,"Meme, TikTok and others"
ওরে জেলে নিয়া পুটকি দিয়া বীর্য ডুকাইয়া মাস পরে পেট কেটে পুতুল ডুকাইয়া দেন,0,"Meme, TikTok and others"
কল করেন জানিও,0,"Meme, TikTok and others"
ও যে যায়গাতে ছিল ওটাই ওর আসল যায়গা ছিল অত বড়ো যায়গা ওকে মানায় না,0,"Meme, TikTok and others"
আমি বিয়ে করব অপু বিশ্বাসকে,0,"Meme, TikTok and others"
এ কথার ভিওিতে ধইরা নিছে শাকিব বিএনপিতে যোগ দিছে হাসতে হাসতে পেট ব্যাথা হয়ে গেল,0,"Meme, TikTok and others"
বস কি মানুষ জানে তর বাবা সয়তানতই সয়তান,0,"Meme, TikTok and others"
ভারত মাতা কি জয়,0,"Meme, TikTok and others"
যতসব ফালতু কথানিজের কথা চিন্তা কর ব্যাটা,0,"Meme, TikTok and others"
ভারতকে ধুয়ে দিয়েছে মানে আবাল নাকি,0,"Meme, TikTok and others"
অন্যায় বিচার করলেন সুপরিন কোট,0,"Meme, TikTok and others"
ছেলে গুলো খাল দুধের দিকে তাকাই,0,"Meme, TikTok and others"
কটোর শাস্তি দেওয়া হোক,0,"Meme, TikTok and others"
কত,0,"Meme, TikTok and others"
ঠিক বলেছেন আপু আপনার কথা গুলো সব উচিত কথা বাংলাদেশের সবার একথা বুঝা উচিৎ ছিল এখন ও সময় আছে সাকিব অপুকে এক সাথে জুটি বাঁধতে সাহায্য করোন,0,"Meme, TikTok and others"
অবশ্যই মা বাবাকে মারা অনেক খারাপ কাজ কিন্তু একটা জিনিস খেয়াল করুন মা ও বাবার উসিলায় পৃথিবীতে আসা একটা উসিলার জন্য আমাদের এত খারাপ লাগে যিনি আমাদের এবং আমাদের মা বাবা কে সৃষ্টি করেছেন তাকে ভুলে অন্য কোন কিছুর প্রার্থনা করি তখন আমাদের সৃষ্টিকর্তার কতটা খারাপ লাগেঠিক তেমন যেমন নিজের মা বাবা কে সামনে রেখে তাদের বাদ দিয়ে শুধু শশুর শাশুড়ি কে মা বাবার স্থান দিয়ে শুধু তাদেরই মাবাবা ডাকা ও মান্য করা,0,"Meme, TikTok and others"
পাডার পাে পাডা,0,"Meme, TikTok and others"
হেডিং এ দেওয়া আছে ভারতের সেনাদের পলায়ন আমি ভারতীয় হয়ে বলছি ভারতীয় সেনারা কখনো পলায়ন করে না তারা সবসময় তারা করে,0,"Meme, TikTok and others"
আমার কাছে উনি রাইট ইসলাম ধর্ম নিয়া বাজে কথা না বল্লে বাকি সব রাইট,0,"Meme, TikTok and others"
এই মেয়ে দোষী এই মেয়ে কে রিমান্ডে নিলে সব বেরেয়ে আসবে আর খুনিদের কে ফাঁসি চাই,0,"Meme, TikTok and others"
বাউ রে বাউ,0,"Meme, TikTok and others"
খবৱটা শুনে ওনেক খুসি হইলাম ওপুকে মেনেনাও,0,"Meme, TikTok and others"
এও ঢপ,0,"Meme, TikTok and others"
যৌবন ও চিরস্থায়ী নয় কোথায় সেই ময়ূরী সময় গেলে সাধন হবেনা সময় থাকতে হাল ধরো,0,"Meme, TikTok and others"
আপনার ব্রা সাইজ কি নাকি,0,"Meme, TikTok and others"
সাকিব খাঁন বলে কথা কারণ সে রিয়েল সুপারস্টার বড় মনের মানুষ,0,"Meme, TikTok and others"
বিজেপির কারন ভারত ধংস হবে ইনশাআল্লাহ,0,"Meme, TikTok and others"
আপু বিয়া করবানা,0,"Meme, TikTok and others"
চাচা আপনার কি মাথার সমস্যা আছে নাকি,0,"Meme, TikTok and others"
আমি ছাই ছেলেকে যেন আইনের আয়াতায় আনে পুলিশ পশাশোন,0,"Meme, TikTok and others"
ইউটিউবের খবরগুলি শুনতে আর ভালো লাগেনা কারন হলো আলা জিহবা ছাড়া মানুষের কথাবার্তা গুলি শুনলেই শরীরে রাগ উঠে যায়,0,"Meme, TikTok and others"
ফালি চাই,0,"Meme, TikTok and others"
পাকিস্তান জিন্দাবাদভারত মুরদাবাদ,0,"Meme, TikTok and others"
এই লোকের বার বছর ছেল হওয়া উচিত,0,"Meme, TikTok and others"
আমার মনে হচ্ছে মেনে নেয়া উচিত,0,"Meme, TikTok and others"
আমি ধন্যবাদ জানাই আইনপসাসনকে,0,"Meme, TikTok and others"
কাসমির কাসমিরই নিজশ্যই সাদিন হওয়ার দরকার,0,"Meme, TikTok and others"
কলমি পিলিজ আপু মনি অনেক কিওট লাগছে,0,"Meme, TikTok and others"
আমি পাকিস্তান এর সাথে জড়িত,0,"Meme, TikTok and others"
]

labels = (
    [0]*40 +   # Normal
    [1]*30 +   # Offensive
    [2]*30     # Hate
)

df = pd.DataFrame({
    "text": texts,
    "label": labels
})

df.to_csv("bangla_hate_dataset.csv", index=False)

df.head()


SyntaxError: invalid character '।' (U+0964) (ipython-input-450985034.py, line 8)

In [ ]:
text = "তুমি খুব ভালো কাজ করেছ"

inputs = tokenizer(text, return_tensors="pt").to(device)
outputs = model(**inputs)

prediction = torch.argmax(outputs.logits, dim=1).item()

labels_map = {
    0: "Normal",
    1: "Offensive",
    2: "Hate Speech"
}

print("Prediction:", labels_map[prediction])